    The cell directly below is the one in which you should make changes
    Only change things to the right of the '=' sign. 
    Note that the '#' symbol means a comment -- when the code runs, it ignores this.

    You can change the scenario name, number of warehouses, the distance band, the fixed warehouses,
    and whether you draw the maps for visualization purposes.

    To Run, go to the menu item 'Cell' and select 'Run All'
    To see the results of the run: 
        Go to the directory where you put this file and you'll see two output files.
        One output file will be the summary and one will have details.
        Tabs will open if you decide to visualize the input and output on maps.
        
    Note it may take up to 20 minutes for the most computationally complex scenario to run (best 5 warehouses)
    and up to 5 minutes for the other scenarios.

In [1]:
# You should change the name to the right of the '=' sign. This names each scenario. 
# If you don't change it, you'll overwrite the files when you run.  Don't put spaces in the name
# And, keep the single quotes in the name.  

scenario_name = 'scenario_1'  #<<<----- you can change this name

# Respective fraction of demand assigned to LTL and TL modes of transportation
LTL_share = .65
TL_share = .35

# Respective rates for each mode of transportation 
TL_pertonmile_fixed = .11
LTL_pertonmile_fixed = .30
TL_pertonmin = 12.5
LTL_pertonmin = 24

distance_band = 300 #<----- you can change this to study the respective percentages of customers which fall within a certain distance of a warehouse

number_of_whs = 3 #<<<----- you can change this to run different scenarios in conjunction with "fix_warehouses"
fix_warehouses = True #<<<----- you can change this to True to fix warehouses to account for different scenarios
fixed_warehouses = ["Seattle", "Dallas", "Pittsburgh"] #<<<----- put the names of the warehouses you'd like to fix here as ['wh1', wh2',...]

# If you don't want either the input or output map to draw, type False with a capital F instead of True
input_map = True   #<<<----- you can change these from True to False
output_map = True

In [2]:
#This is code to start running the model.  You don't need to interact with this
from pulp import *
import time
import numpy as np
import pandas as pd
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go

In [3]:
# This model minimizes total cost by finding the optimal locations of warehouses and the optimal flow between warehouses and customers
def optimal_warehouses(warehouses, customers, distance, costs_TL, costs_LTL, number_of_whs, fixed_warehouse_ids, distance_band, active_warehouses):
    start_time=time.time()
    # Create the "TL_LTL_problem" variable to contain the problem data
    TL_LTL_problem = LpProblem("TL_LTL_problem", LpMinimize)
    
    # A dictionary called warehouse_vars is created to contain decision variables specifying whether or not a warehouse should be built in a location
    warehouse_vars = LpVariable.dicts("Open", [w for w in active_warehouses], cat = 'Binary')
    
    # Flow variables are created to specify the amount of flow from warehouses from customers, note this is continuous since product must be divided into TL and LTL
    TL_flow_vars = LpVariable.dicts("Flow TL", [(w, c) for w in active_warehouses for c in customers], lowBound = 0)
    LTL_flow_vars = LpVariable.dicts("Flow LTL", [(w, c) for w in active_warehouses for c in customers], lowBound = 0)
    
    # The objective function is added to the problem first
    total_cost = lpSum([costs_TL[w,c]*TL_flow_vars[w,c]/2000 + costs_LTL[w,c]*LTL_flow_vars[w,c]/2000 for w in active_warehouses for c in customers])
    
    # Here we have 5 types of constraints
    
    """
    
    A Pulp LP constraint: LpConstraint(e, sense, name, rhs)
    Parameters:	
    e – an instance of LpExpression
    sense – one of LpConstraintEQ, LpConstraintGE, LpConstraintLE
    name – identifying string
    rhs – numerical value of constraint right hand side
    """
    
    # All demand must be met
    for c in customers:
        TL_LTL_problem += LpConstraint(e = lpSum([TL_flow_vars[w,c] + LTL_flow_vars[w,c] for w in active_warehouses]), 
                            sense=LpConstraintEQ, 
                            name=str(c)+"_Served", 
                            rhs = customers[c][3])
 
    # Ensures that total # warehouses doesn't exceed maximum
    TL_LTL_problem += LpConstraint(e = lpSum([warehouse_vars[w] for w in active_warehouses]), 
                        sense=LpConstraintLE,
                        name="Warehouse Count",
                        rhs = number_of_whs)

    # Fixes warehouses that must be built if "fix_warehouses" set to true
    if fix_warehouses == True:
        for warehouse in fixed_warehouse_ids:
            TL_LTL_problem += LpConstraint(e = warehouse_vars[warehouse],
                                sense=LpConstraintEQ,
                                name=str(warehouse)+"_Fixed",
                                rhs=1)     
    
    # Each customer must individually receive the respective TL and LTL shares of demand
    for c in customers:
        TL_LTL_problem += LpConstraint(e = lpSum([TL_flow_vars[w,c] for w in active_warehouses]),
                            sense=LpConstraintGE,
                            name=str(c)+"TL_demand",
                            rhs = TL_share*customers[c][3])
    
        TL_LTL_problem += LpConstraint(e = lpSum([LTL_flow_vars[w,c] for w in active_warehouses]),
                            sense=LpConstraintGE,
                            name=str(c)+"LTL_demand",
                            rhs = LTL_share*customers[c][3])
        
    for warehouse in active_warehouses:
        for customer in customers:
            TL_LTL_problem += LpConstraint(e = TL_flow_vars[warehouse,customer] - TL_capacity * warehouse_vars[warehouse],
                                sense=LpConstraintLE,
                                name=str(warehouse)+"TL_open"+str(customer),
                                rhs = 0)
    
            TL_LTL_problem += LpConstraint(e = LTL_flow_vars[warehouse,customer] - LTL_capacity * warehouse_vars[warehouse],
                                sense=LpConstraintLE,
                                name=str(warehouse)+"LTL_open"+str(customer),
                                rhs = 0)
            

    # Setting problem objective
    TL_LTL_problem.setObjective(total_cost)
    
    # The problem data is written to an .lp file
    TL_LTL_problem.writeLP("TL_LTL_prob.lp")
    
    # The problem is solved using PuLP's choice of Solver
    TL_LTL_problem.solve()
    
    # Print and log status of solution
    file.write('\nstatus:'+ LpStatus[TL_LTL_problem.status])
    print("Optimization Status",LpStatus[TL_LTL_problem.status] )  #print in Jupyter Notebook
    
    total_demand = sum(customers[c][3] for c in customers)
    total_demand_in_tons = total_demand * 2000
    
    print ("Total Demand in tons",total_demand_in_tons)
    file.write("\nTotal Demand:"+ str(total_demand_in_tons))
    print("Objective: ", value(TL_LTL_problem.objective))
    file.write("\nObjective: "+ str(value(TL_LTL_problem.objective)))
    print("Average cost per ton: ",round(value(TL_LTL_problem.objective)/total_demand_in_tons,1),"$")
    file.write("\nAverage cost per ton: "+str(round(value(TL_LTL_problem.objective)/total_demand_in_tons,1))+"$")
    
    end_time = time.time()
    time_diff = end_time - start_time
    file.write("\nRun Time of model in seconds {:.1f}" .format(time_diff))
    print("Run Time of model in seconds {:.1f}" .format(time_diff))
    
    #preparing data to write in excel sheets
    opened_warehouses = []
    for w in warehouse_vars.keys():
        if(warehouse_vars[w].varValue > 0):
            wh = {
                'Warehouse Key': w,
                'Warehouse City':warehouses[w][0],
                'Lat':warehouses[w][1],
                'Lon':warehouses[w][2],
            }
            opened_warehouses.append(wh)
                      
    # Converting the list to dataframe        
    df_wh = pd.DataFrame.from_records(opened_warehouses)
    
    df_wh = df_wh[['Warehouse Key', 'Warehouse City']]
    list_warehouses_open = list(df_wh['Warehouse Key'])
    
    # Writing detailed files
    df_wh.to_excel(writer,'Opened Warehouses',index=False)
    
    dist_count = 0
    percent_count = 0
    customers_assignment = []   
    for (w,c) in TL_flow_vars.keys():
        if TL_flow_vars[(w,c)].varValue > 0:
            cust = {'Warehouse':warehouses[w][0],
                    'TL_Customer':customers[c][0],
                    'TL_Flow': TL_flow_vars[(w,c)].varValue,
                    'Distance': distance[w,c],
                    'Warehouse Latitude': warehouses[w][1],
                    'Warehouse Longitude': warehouses[w][2],
                    'Customer Latitude': customers[c][1],
                    'Customer Longitude': customers[c][2]
                    }
            customers_assignment.append(cust)
            dist_count += TL_flow_vars[w,c].varValue*distance[w,c]
            if distance[w,c] <= distance_band:
                percent_count += TL_flow_vars[w,c].varValue
                
    df_cu = pd.DataFrame.from_records(customers_assignment)
    df_cu_copy = df_cu.copy()
    df_cu_copy = df_cu[['Warehouse', 'TL_Customer', 'Distance', 'TL_Flow']]
    df_cu_copy.to_excel(writer,'Customers Assignment',index=False)
    
    
    
    customers_assignment = []   
    for (w,c) in LTL_flow_vars.keys():
        if LTL_flow_vars[(w,c)].varValue > 0:
            cust = {'Warehouse':warehouses[w][0],
                    'LTL_Customer':customers[c][0],
                    'LTL_Flow': LTL_flow_vars[(w,c)].varValue,
                    'Distance': distance[w,c],
                    'Warehouse Latitude': warehouses[w][1],
                    'Warehouse Longitude': warehouses[w][2],
                    'Customer Latitude': customers[c][1],
                    'Customer Longitude': customers[c][2]
                    }
            customers_assignment.append(cust)
            dist_count += LTL_flow_vars[w,c].varValue*distance[w,c]
            if distance[w,c] <= distance_band:
                percent_count += LTL_flow_vars[w,c].varValue
            
    avg_distance_to_customers = dist_count/total_demand
    percentage = percent_count/total_demand * 100
    print("The average distance to customers is: ", avg_distance_to_customers)
    file.write("\nThe average distance to customers is: "+str(avg_distance_to_customers))
    print("The percentage of customers within {} miles is: ".format(distance_band), percentage)
    file.write("\nThe percentage of customers within {} miles is: ".format(distance_band)+str(percentage))
    
    df_cu_2 = pd.DataFrame.from_records(customers_assignment)
    df_cu_2_copy = df_cu_2.copy()
    df_cu_2_copy = df_cu_2[['Warehouse', 'LTL_Customer', 'Distance', 'LTL_Flow']]
    df_cu_2_copy.to_excel(writer,'Customers Assignment',index=False)

    return df_cu, df_cu_2, list_warehouses_open

In [4]:
#  This is the input data.  In a normal project, you would load this from another file.  We are making it simple by packaging it here 
def get_data():
    #Warehouses
    #id: (name, lat, long, active)
    warehouses = {1: ('Albany', 42.65287, -73.74868, True),
     2: ('Albuquerque', 35.082729, -106.646276, False),
     3: ('Atlanta', 33.753693, -84.389544, True),
     4: ('Augusta', 33.432493, -81.955568, False),
     5: ('Baltimore', 39.294398, -76.622747, True),
     6: ('Baton Rouge', 30.449314, -91.187593, True),
     7: ('Birmingham', 33.518634, -86.808862, False),
     8: ('Boston', 42.36097, -71.05344, True),
     9: ('Buffalo', 42.896219, -78.884649, False),
     10: ('Charleston', 32.778908, -79.937993, False),
     11: ('Charlotte', 35.194361, -80.826397, True),
     12: ('Chattanooga', 35.028175, -85.152348, False),
     13: ('Chicago', 41.88331, -87.624713, True),
     14: ('Cincinnati', 39.10663, -84.49974, False),
     15: ('Columbus', 40.099395, -83.016823, True),
     16: ('Dallas', 32.787642, -96.799525, True),
     17: ('Denver', 39.75071, -104.996225, True),
     18: ('Des Moines', 41.604425, -93.631016, False),
     19: ('Detroit', 42.346577, -83.059731, False),
     20: ('Dover', 39.147003, -75.480883, False),
     21: ('El Paso', 31.760613, -106.47948, False),
     22: ('Fresno', 36.749611, -119.786244, False),
     23: ('Grand Rapids', 42.965899, -85.654579, False),
     24: ('Houston', 29.757317, -95.365005, False),
     25: ('Indianapolis', 39.77422, -86.109309, True),
     26: ('Jackson', 32.289153, -90.184021, False),
     27: ('Kansas City', 39.103883, -94.600613, True),
     28: ('Las Vegas', 36.17269, -115.121117, True),
     29: ('Louisville', 38.14326, -85.69578, True),
     30: ('Little Rock', 34.747348, -92.278932, False),
     31: ('Los Angeles', 33.974044, -118.248849, True),
     32: ('Memphis', 35.033731, -89.934319, True),
     33: ('Miami', 25.778271, -80.198105, False),
     34: ('Milwaukee', 43.037602, -87.916246, False),
     35: ('Minneapolis', 44.985775, -93.270165, False),
     36: ('Mobile', 30.692504, -88.04323, False),
     37: ('Nashville', 36.164003, -86.7745, False),
     38: ('New York', 40.75012, -73.997846, True),
     39: ('Oklahoma City', 35.467763, -97.520977, False),
     40: ('Omaha', 41.263251, -95.932956, False),
     41: ('Orlando', 28.541627, -81.37397, True),
     42: ('Philadelphia', 39.961558, -75.199624, True),
     43: ('Phoenix', 33.451015, -112.068554, True),
     44: ('Pittsburgh', 40.474802, -79.95449, True),
     45: ('Portland', 45.498251, -122.692496, True),
     46: ('Raleigh', 35.773856, -78.634051, False),
     47: ('Reno', 39.526866, -119.811392, True),
     48: ('Richmond', 37.538812, -77.436395, False),
     49: ('Sacramento', 38.585076, -121.491186, False),
     50: ('Salt Lake City', 40.755074, -111.89849, True),
     51: ('San Antonio', 29.469324, -98.527988, False),
     52: ('San Diego', 32.724693, -117.164885, False),
     53: ('San Francisco', 37.779887, -122.418066, True),
     54: ('Sarasota', 27.337217, -82.51411, False),
     55: ('Seattle', 47.611601, -122.333038, True),
     56: ('Spokane', 47.66517, -117.435008, False),
     57: ('St. Louis', 38.631358, -90.192246, False),
     58: ('Tampa', 27.95454, -82.45734, False),
     59: ('Tucson', 32.216256, -110.970728, False),
     60: ('Wichita', 37.686354, -97.334936, False)}
    
    # Customers
    #id: (name, lat, long, active)
    customers = {109: (35215, 33.639053, -86.691875, 746708), 872: (85008, 33.469624, -111.998569, 1363257), 873: (85009, 33.456603, -112.123087, 1380133), 877: (85015, 33.507977, -112.101173, 719920), 879: (85017, 33.510589, -112.122065, 930870), 884: (85022, 33.627465, -112.051962, 1026634), 889: (85029, 33.59741, -112.118455, 874101), 891: (85032, 33.619208, -112.004108, 1097551), 892: (85033, 33.490937, -112.213503, 856760), 894: (85035, 33.473497, -112.187607, 1103373), 896: (85040, 33.408851, -112.026341, 975290), 903: (85051, 33.560619, -112.134084, 827662), 909: (85201, 33.430515, -111.840854, 900427), 910: (85202, 33.38223, -111.867598, 623398), 912: (85204, 33.401183, -111.790791, 1339123), 913: (85205, 33.437801, -111.714585, 910695), 916: (85208, 33.390705, -111.648725, 995117), 926: (85224, 33.321325, -111.877926, 753611), 927: (85225, 33.31629, -111.831035, 1549048), 948: (85254, 33.616346, -111.954949, 774598), 961: (85281, 33.422399, -111.927588, 1168769), 962: (85282, 33.39087, -111.925598, 1092419), 963: (85283, 33.365103, -111.928523, 951456), 967: (85301, 33.536288, -112.176745, 1152599), 974: (85308, 33.651823, -112.167339, 1223482), 998: (85345, 33.569542, -112.246397, 933609), 1014: (85364, 32.701076, -114.646859, 1563553), 1086: (85705, 32.26608, -110.99898, 1128237), 1087: (85706, 32.1177, -110.8941, 1448865), 1089: (85710, 32.21416, -110.82923, 1065507), 1090: (85711, 32.218469, -110.887678, 958955), 1092: (85713, 32.19144, -111.0627, 821214), 1097: (85719, 32.241787, -110.946837, 800730), 1107: (85746, 32.082299, -111.092793, 745052), 1387: (72032, 35.067299999999996, -92.38080000000001, 1192124), 1554: (72401, 35.824808, -90.697175, 1158871), 1827: (90001, 33.97331, -118.243612, 1085463), 1828: (90002, 33.948432, -118.245196, 795177), 1829: (90003, 33.962989, -118.272517, 1040369), 1830: (90004, 34.076333, -118.307713, 1522222), 1831: (90005, 34.055509, -118.30922, 838284), 1832: (90006, 34.045817, -118.290338, 1564916), 1833: (90007, 34.026525, -118.282408, 840623), 1836: (90011, 34.006146, -118.257237, 2266470), 1841: (90016, 34.027729, -118.351874, 886803), 1843: (90018, 34.030481, -118.318046, 1100400), 1844: (90019, 34.048281, -118.342487, 1339145), 1845: (90020, 34.068259, -118.31043, 859283), 1847: (90022, 34.022686, -118.152363, 1188113), 1848: (90023, 34.025925, -118.20065700000002, 849582), 1849: (90024, 34.060189, -118.4364, 960351), 1850: (90025, 34.044073, -118.451381, 632223), 1851: (90026, 34.079313, -118.262692, 1216315), 1852: (90027, 34.12356, -118.28784, 1132455), 1854: (90029, 34.090213, -118.293835, 876137), 1856: (90032, 34.080616, -118.174263, 883713), 1857: (90033, 34.049807, -118.209245, 830434), 1858: (90034, 34.028026, -118.399267, 976104), 1861: (90037, 34.000915, -118.288342, 1026187), 1866: (90042, 34.118577, -118.189925, 1291778), 1867: (90043, 33.990206, -118.335759, 1015140), 1868: (90044, 33.956268, -118.290701, 1734990), 1870: (90046, 34.105576, -118.36679399999998, 803120), 1871: (90047, 33.953467, -118.311177, 833663), 1875: (90057, 34.060269, -118.276734, 1029744), 1880: (90063, 34.042454, -118.184723, 1242082), 1882: (90065, 34.10598, -118.229781, 777386), 1883: (90066, 33.993713, -118.42832, 1178588), 1889: (90201, 33.969157, -118.172903, 2105688), 1893: (90220, 33.890694, -118.239135, 1077308), 1894: (90221, 33.87954, -118.20054, 989992), 1899: (90241, 33.940169, -118.129391, 822319), 1900: (90242, 33.924064, -118.145732, 846509), 1902: (90247, 33.888193, -118.295204, 747529), 1905: (90250, 33.9153, -118.351309, 2130619), 1907: (90255, 33.980311, -118.209874, 1431004), 1910: (90262, 33.925084, -118.198182, 1477208), 1917: (90275, 33.76666699999999, -118.366667, 859034), 1920: (90280, 33.941262, -118.193702, 2063012), 1935: (90501, 33.829914, -118.314527, 821087), 1937: (90503, 33.842791, -118.357275, 855891), 1946: (90620, 33.843903, -118.007993, 1077252), 1949: (90630, 33.818073, -118.035677, 1074273), 1950: (90631, 33.94104, -117.95442, 1208731), 1951: (90638, 33.906013, -118.005828, 1180754), 1952: (90640, 34.015369, -118.111726, 1251024), 1953: (90650, 33.908151, -118.080822, 2441429), 1954: (90660, 33.988063, -118.088143, 1167043), 1958: (90703, 33.866635, -118.048458, 777819), 1960: (90706, 33.888756, -118.128543, 1698121), 1968: (90723, 33.897236, -118.160018, 1077265), 1969: (90731, 33.74352, -118.27944, 1271876), 1974: (90744, 33.791522, -118.252215, 1017717), 1975: (90745, 33.820353, -118.266179, 947542), 1979: (90804, 33.776725, -118.14614999999999, 656726), 1980: (90805, 33.863555, -118.182163, 1926746), 1981: (90806, 33.805737, -118.181738, 899122), 1985: (90813, 33.778685, -118.191698, 1362114), 1994: (91016, 34.143769, -117.999476, 655717), 2011: (91205, 34.135443, -118.24258, 697287), 2019: (91304, 34.218348, -118.62584699999998, 910016), 2020: (91306, 34.207991, -118.57547, 690339), 2029: (91331, 34.252512, -118.42534900000001, 1543338), 2030: (91335, 34.199469, -118.539891, 1610682), 2032: (91342, 34.303046, -118.42194, 1420758), 2033: (91343, 34.237131, -118.481042, 1206820), 2034: (91344, 34.279812, -118.500354, 785279), 2036: (91350, 34.48502200000001, -118.42802000000003, 947512), 2037: (91351, 34.425819, -118.443437, 1088907), 2038: (91352, 34.224912, -118.36035, 699467), 2042: (91360, 34.208451, -118.874426, 666119), 2050: (91401, 34.176265, -118.42762599999999, 966687), 2051: (91402, 34.222187, -118.442663, 1356813), 2053: (91405, 34.201681, -118.446452, 1113796), 2054: (91406, 34.201751, -118.492685, 1089291), 2066: (91605, 34.209647, -118.40255, 888984), 2067: (91606, 34.186265, -118.391357, 1079924), 2071: (91702, 34.124881, -117.903021, 1274590), 2072: (91706, 34.085581, -117.970122, 1797507), 2073: (91709, 33.98664, -117.68322, 1654036), 2074: (91710, 34.016105, -117.686207, 1225134), 2080: (91730, 34.09914, -117.58128, 1249685), 2082: (91732, 34.074497, -118.011309, 1067410), 2083: (91733, 34.051383, -118.04458800000002, 1031315), 2089: (91744, 34.028223, -117.937998, 1639634), 2090: (91745, 33.998974, -117.965163, 1070508), 2092: (91748, 33.979568, -117.89843700000002, 1126243), 2098: (91761, 34.036901, -117.606236, 882877), 2099: (91762, 34.058501, -117.667472, 1136335), 2101: (91764, 34.077008, -117.617165, 806470), 2102: (91765, 34.001426, -117.815685, 731393), 2103: (91766, 34.041268, -117.761339, 1115177), 2104: (91767, 34.081648, -117.740882, 840117), 2106: (91770, 34.065846, -118.082058, 1106950), 2112: (91786, 34.10366, -117.661893, 738480), 2113: (91789, 34.014965, -117.856127, 945584), 2114: (91790, 34.065225, -117.938282, 857740), 2117: (91801, 34.089881, -118.129539, 1339043), 2123: (91910, 32.625054, -117.013699, 1684871), 2124: (91911, 32.60808, -117.053163, 1763544), 2134: (91941, 32.759711, -116.997713, 807210), 2138: (91950, 32.66865, -117.091284, 1084634), 2141: (91977, 32.72207, -116.993911, 1264757), 2148: (92009, 33.099272, -117.270924, 760566), 2150: (92019, 32.782189, -116.908056, 1013645), 2151: (92020, 32.793886, -116.965928, 986418), 2152: (92021, 32.81871, -116.901089, 1525478), 2153: (92024, 33.055326, -117.263733, 792268), 2154: (92025, 33.098448, -117.084591, 1191226), 2155: (92026, 33.1741, -117.101925, 771535), 2156: (92027, 33.138222, -117.045024, 988069), 2157: (92028, 33.36866, -117.219178, 859905), 2160: (92037, 32.838775, -117.253243, 969946), 2161: (92040, 32.861292, -116.915988, 911658), 2162: (92054, 33.205217, -117.352732, 1798387), 2163: (92056, 33.21463, -117.289157, 951001), 2164: (92057, 33.240638, -117.298443, 1107084), 2168: (92064, 32.980878, -117.036369, 740672), 2172: (92069, 33.149519, -117.173018, 1079521), 2174: (92071, 32.846307, -116.988769, 1002594), 2178: (92083, 33.190177, -117.234888, 1131545), 2179: (92084, 33.215973, -117.217092, 1104152), 2183: (92102, 32.716263, -117.11426, 1126045), 2185: (92104, 32.740029, -117.130447, 1030697), 2186: (92105, 32.740294, -117.091575, 1117968), 2190: (92109, 32.791495, -117.236899, 978398), 2192: (92111, 32.800458, -117.171574, 820145), 2193: (92113, 32.697656, -117.117688, 729144), 2194: (92114, 32.70713, -117.051153, 1168238), 2195: (92115, 32.761679, -117.070858, 1368076), 2197: (92117, 32.824555, -117.200178, 1203846), 2205: (92126, 32.912763, -117.148011, 1297950), 2207: (92128, 33.010498, -117.070512, 894140), 2208: (92129, 32.966476, -117.119682, 1081407), 2212: (92154, 32.578188, -117.072374, 1551608), 2214: (92201, 33.707812, -116.231849, 911296), 2225: (92234, 33.822485, -116.462762, 1052218), 2231: (92243, 32.784553, -115.571017, 718185), 2278: (92324, 34.03242, -117.2823, 937340), 2284: (92335, 34.093648, -117.460417, 1421015), 2285: (92336, 34.132487, -117.459265, 1277733), 2291: (92345, 34.416478, -117.307226, 1407854), 2292: (92346, 34.129046, -117.19692, 1197914), 2307: (92376, 34.117034, -117.376352, 1441662), 2313: (92392, 34.510298, -117.31839, 1050702), 2317: (92399, 34.033763, -117.040299, 724252), 2319: (92404, 34.14831, -117.257233, 1168399), 2321: (92407, 34.183703, -117.34251900000001, 1134605), 2323: (92410, 34.105653, -117.294667, 818687), 2326: (92503, 33.914455, -117.45606, 1705200), 2327: (92504, 33.924842, -117.397533, 867898), 2329: (92506, 33.940143, -117.361737, 980366), 2330: (92507, 33.976325, -117.330414, 854049), 2332: (92509, 33.996714, -117.44577499999998, 1372958), 2344: (92553, 33.908611, -117.238598, 981097), 2346: (92557, 33.964589, -117.263935, 855522), 2361: (92592, 33.505961, -117.00392, 881796), 2368: (92612, 33.648309, -117.821853, 1006490), 2374: (92626, 33.680139, -117.908452, 1028357), 2375: (92627, 33.64828, -117.915538, 1098009), 2377: (92630, 33.64578, -117.66912, 989785), 2378: (92646, 33.665392, -117.968576, 912401), 2379: (92647, 33.72103, -118.003329, 1302066), 2380: (92648, 33.677256, -118.005064, 863770), 2383: (92653, 33.601535, -117.711678, 903227), 2385: (92656, 33.57612, -117.73638, 842564), 2395: (92677, 33.52554, -117.71436, 1474914), 2397: (92683, 33.750865, -117.989463, 1801653), 2398: (92688, 33.651232, -117.59383399999999, 944752), 2399: (92691, 33.612814, -117.662215, 1068621), 2400: (92692, 33.614433, -117.64327299999998, 876291), 2402: (92701, 33.752342, -117.854139, 1340391), 2403: (92703, 33.748904, -117.907165, 1670693), 2404: (92704, 33.724888, -117.908994, 2240710), 2405: (92705, 33.753989, -117.791852, 1044356), 2407: (92707, 33.69678, -117.87012, 1004831), 2408: (92708, 33.71665, -117.944594, 1165832), 2409: (92780, 33.736361, -117.822888, 889292), 2411: (92801, 33.842832, -117.954595, 1259620), 2412: (92802, 33.808505, -117.922777, 851465), 2413: (92804, 33.818606, -117.972857, 1368280), 2414: (92805, 33.835916, -117.908583, 1425254), 2422: (92833, 33.876643, -117.955051, 736771), 2424: (92840, 33.786931, -117.927259, 1187169), 2426: (92843, 33.767061, -117.929, 901329), 2433: (92867, 33.811025, -117.849274, 862386), 2436: (92870, 33.874415, -117.854269, 1167854), 2437: (92879, 33.880653, -117.537555, 785458), 2440: (92882, 33.862585, -117.598903, 973462), 2445: (93003, 34.270548, -119.217135, 1089463), 2447: (93010, 34.228608, -119.02255, 943773), 2454: (93030, 34.214999, -119.179607, 1472844), 2455: (93033, 34.168245, -119.16567, 1456282), 2460: (93063, 34.271667, -118.708056, 772553), 2461: (93065, 34.268961, -118.769487, 1504569), 2471: (93117, 34.437147, -119.866076, 1146505), 2492: (93230, 36.329023, -119.641214, 1230464), 2511: (93257, 36.069871, -119.021504, 988121), 2523: (93274, 36.208357, -119.341083, 1398064), 2525: (93277, 36.312162, -119.307419, 895465), 2535: (93304, 35.34985, -119.024721, 860124), 2537: (93306, 35.390652, -118.93041, 923884), 2538: (93307, 35.316665, -118.975058, 993653), 2539: (93308, 35.54676, -119.04402, 961158), 2540: (93309, 35.337074, -119.070042, 1227390), 2542: (93312, 35.38677, -119.173597, 983540), 2559: (93436, 34.651186, -120.435893, 829055), 2575: (93458, 34.952802, -120.431903, 787795), 2599: (93535, 34.71549099999999, -117.902577, 1140958), 2600: (93536, 34.775252, -118.47169699999999, 894678), 2607: (93550, 34.568461, -118.062387, 1380106), 2627: (93611, 36.845587, -119.652237, 861554), 2647: (93638, 36.974268, -120.002242, 1078286), 2674: (93702, 36.740431, -119.756053, 965532), 2681: (93720, 36.864207, -119.763501, 943338), 2683: (93722, 36.796753, -119.882901, 1489390), 2686: (93727, 36.753992, -119.698212, 1305368), 2689: (93905, 36.680613, -121.618316, 958690), 2690: (93906, 36.709565, -121.639635, 1196252), 2713: (94010, 37.570237, -122.360344, 796213), 2714: (94014, 37.68948, -122.43936, 991102), 2715: (94015, 37.679341, -122.483788, 1402277), 2739: (94080, 37.652366, -122.430543, 1294579), 2740: (94086, 37.3772, -122.019178, 1297819), 2741: (94087, 37.348182, -122.031788, 878994), 2749: (94109, 37.794508, -122.418244, 1213998), 2750: (94110, 37.748224, -122.415699, 1791977), 2752: (94112, 37.721519, -122.439949, 1500145), 2755: (94116, 37.741108, -122.485687, 876864), 2758: (94121, 37.77977, -122.489312, 877496), 2759: (94122, 37.760276, -122.482029, 1355066), 2769: (94134, 37.722221, -122.411294, 873181), 2771: (94303, 37.44936, -122.12525999999998, 725675), 2779: (94501, 37.760574, -122.260375, 906988), 2784: (94509, 37.995169, -121.803953, 1418483), 2800: (94533, 38.285247, -122.008109, 1461292), 2802: (94536, 37.562573, -121.997844, 1327452), 2803: (94538, 37.526834, -121.965639, 1199422), 2804: (94539, 37.517314, -121.929678, 1139506), 2805: (94541, 37.673394, -122.081227, 1246911), 2807: (94544, 37.634255, -122.063172, 1468829), 2809: (94546, 37.72608, -122.08038, 751319), 2812: (94550, 37.681436, -121.753052, 1191215), 2814: (94553, 37.99128, -122.16432000000002, 1105556), 2817: (94558, 38.343537, -122.305067, 1116471), 2819: (94560, 37.535958, -122.031512, 776889), 2823: (94565, 38.017076, -121.90965, 1541668), 2832: (94577, 37.718789, -122.158712, 1038905), 2836: (94583, 37.751779, -121.953457, 921865), 2839: (94587, 37.594129, -122.047013, 1112404), 2841: (94589, 38.16234, -122.2494, 1007178), 2843: (94591, 38.101456, -122.210632, 1020351), 2846: (94596, 37.904944, -122.054411, 959913), 2849: (94601, 37.780584, -122.216306, 1317846), 2852: (94605, 37.762699, -122.16, 751298), 2853: (94606, 37.79127, -122.243159, 824627), 2876: (94806, 37.972918, -122.333929, 1146760), 2877: (94901, 37.974155, -122.509463, 899297), 2885: (94928, 38.343934, -122.699887, 765440), 2918: (95008, 37.278271, -121.955198, 1024698), 2921: (95014, 37.314123, -122.04441100000001, 1347757), 2925: (95020, 37.019255, -121.574817, 876104), 2926: (95023, 36.848759, -121.388323, 1054232), 2930: (95035, 37.438136, -121.888801, 1562124), 2931: (95037, 37.123009, -121.648882, 829481), 2938: (95051, 37.347073, -121.98335, 872533), 2940: (95060, 36.989018, -122.057824, 1064473), 2947: (95076, 36.941261, -121.78252399999998, 1711231), 2949: (95111, 37.282801, -121.825473, 1352803), 2950: (95112, 37.345558, -121.883995, 1072394), 2952: (95116, 37.352823, -121.849809, 1268800), 2958: (95122, 37.325993, -121.832012, 1325706), 2959: (95123, 37.242541, -121.834674, 1285716), 2960: (95124, 37.256921, -121.922873, 1055949), 2961: (95125, 37.293628, -121.897822, 1113731), 2963: (95127, 37.369641, -121.817818, 1299851), 2968: (95132, 37.406513, -121.855877, 953882), 2976: (95148, 37.329994, -121.792353, 1036840), 2981: (95206, 37.918977, -121.312883, 962294), 2982: (95207, 38.00188, -121.323361, 880477), 2984: (95210, 38.026084, -121.295564, 977521), 3003: (95240, 38.124431, -121.267176, 968968), 3046: (95340, 37.299167, -120.474945, 1310731), 3050: (95350, 37.664246, -120.992352, 1012634), 3051: (95351, 37.629231, -121.008022, 741872), 3053: (95355, 37.675966, -120.944878, 910342), 3069: (95376, 37.732544, -121.418973, 1722017), 3071: (95380, 37.498202, -120.857364, 670070), 3080: (95403, 38.479575, -122.750548, 657332), 3199: (95608, 38.628172, -121.327836, 1092754), 3200: (95610, 38.696835, -121.265911, 971731), 3205: (95616, 38.556431, -121.746377, 1515995), 3209: (95621, 38.697816, -121.311197, 712478), 3215: (95628, 38.65224, -121.255592, 622330), 3217: (95630, 38.683096, -121.16053500000001, 976653), 3249: (95670, 38.60352, -121.24806, 1025181), 3263: (95687, 38.346229, -121.954425, 1252146), 3289: (95758, 38.405311, -121.429597, 1039007), 3301: (95822, 38.511675, -121.493259, 908535), 3302: (95823, 38.481025, -121.444142, 1147025), 3307: (95828, 38.483025, -121.397358, 1258071), 3310: (95831, 38.498299, -121.534017, 660692), 3391: (96003, 40.6572, -122.33682, 938175), 3509: (80010, 39.735849, -104.865186, 933757), 3510: (80011, 39.74165, -104.791421, 931324), 3511: (80012, 39.694487, -104.832515, 890046), 3512: (80013, 39.660246, -104.779822, 1257753), 3514: (80015, 39.624696, -104.7888, 1076253), 3519: (80020, 39.93468, -105.07662, 759412), 3536: (80110, 39.648959999999995, -104.98086, 823873), 3545: (80123, 39.595296, -105.08785999999999, 844740), 3548: (80126, 39.548022, -104.963984, 1394365), 3572: (80219, 39.698319, -105.032695, 1371353), 3581: (80229, 39.8502, -104.96988, 931018), 3583: (80231, 39.675732, -104.886871, 847090), 3601: (80303, 39.991717, -105.2274, 874920), 3656: (80501, 40.166839, -105.134916, 1096990), 3669: (80525, 40.534158, -105.043374, 984877), 3670: (80526, 40.54558, -105.112604, 1047839), 3695: (80631, 40.418082, -104.708389, 886193), 3696: (80634, 40.408834, -104.760402, 854754), 3782: (80906, 38.791623, -104.825814, 945032), 3792: (80918, 38.915062, -104.773227, 769856), 3989: (6010, 41.679705, -72.931387, 1394456), 4008: (6040, 41.777443, -72.524997, 868709), 4031: (6082, 41.986942, -72.565275, 1042957), 4045: (6106, 41.74668, -72.696298, 758668), 4144: (6457, 41.548962, -72.663524, 673922), 4145: (6460, 41.232682, -73.061948, 976725), 4164: (6492, 41.459922, -72.818029, 730277), 4168: (6511, 41.327048, -72.940381, 1020970), 4173: (6516, 41.269511, -72.964339, 1055624), 4181: (6606, 41.21302, -73.211437, 925860), 4228: (6810, 41.389689, -73.454963, 719172), 4248: (6902, 41.054668, -73.543191, 1059225), 4254: (19702, 39.60461, -75.74627, 720326), 4260: (19711, 39.70785, -75.734964, 837880), 4262: (19720, 39.673263, -75.595423, 1309802), 4273: (19805, 39.73164, -75.62424, 861793), 4319: (20002, 38.905231, -76.992743, 1200746), 4326: (20009, 38.917847, -77.035346, 798441), 4328: (20011, 38.949806, -77.015627, 912708), 4334: (20019, 38.890726, -76.938125, 926441), 4335: (20020, 38.86439, -76.971958, 1078800), 4372: (32073, 30.174663, -81.758375, 1183640), 4413: (32174, 29.289955, -81.123815, 989874), 4434: (32210, 30.260733, -81.746664, 1106852), 4447: (32225, 30.348896, -81.50107, 808694), 4452: (32244, 30.223538, -81.757243, 995517), 4463: (32303, 30.483064, -84.32434, 984863), 4465: (32308, 30.503754, -84.212359, 1058164), 4619: (32703, 28.662448, -81.501094, 940782), 4645: (32765, 28.648105, -81.210071, 867158), 4657: (32792, 28.595103, -81.304723, 894963), 4666: (32808, 28.57263, -81.442973, 877154), 4676: (32822, 28.505058, -81.290138, 893301), 4678: (32825, 28.522353, -81.227289, 1060157), 4689: (32839, 28.487458, -81.403507, 934776), 4704: (32935, 28.138545, -80.657969, 739444), 4726: (33010, 25.82898, -80.28564, 720928), 4727: (33012, 25.865517, -80.297427, 1300770), 4730: (33015, 25.940769999999997, -80.315677, 1138623), 4731: (33016, 25.890138, -80.341466, 884983), 4734: (33020, 26.016843, -80.15108, 627440), 4735: (33021, 26.026253, -80.189124, 846772), 4736: (33023, 25.986967999999997, -80.20655999999998, 1144497), 4737: (33024, 26.018669999999997, -80.258199, 1087544), 4738: (33025, 25.992876, -80.274221, 834519), 4756: (33055, 25.943016, -80.276516, 1089437), 4760: (33063, 26.248972999999996, -80.206871, 914805), 4761: (33064, 26.2779, -80.14782, 1213162), 4762: (33065, 26.268784999999998, -80.255243, 1220974), 4765: (33068, 26.216234, -80.216437, 840207), 4773: (33125, 25.781311, -80.236441, 733305), 4774: (33126, 25.774119, -80.290919, 915880), 4790: (33142, 25.811543, -80.237681, 1081999), 4795: (33147, 25.853411, -80.237002, 1135034), 4799: (33155, 25.737315, -80.309137, 970214), 4801: (33157, 25.606686, -80.344992, 999603), 4804: (33161, 25.89093400000001, -80.178037, 1075645), 4805: (33162, 25.92477, -80.1782, 978032), 4806: (33165, 25.729513, -80.360218, 1056709), 4815: (33175, 25.729688, -80.410127, 1253007), 4816: (33176, 25.656255999999992, -80.360854, 899420), 4817: (33177, 25.592736, -80.405844, 695404), 4826: (33186, 25.661132, -80.407574, 1171317), 4830: (33193, 25.693575, -80.445767, 1058704), 4839: (33311, 26.140547, -80.173789, 1021595), 4840: (33312, 26.088164000000003, -80.184514, 1056510), 4841: (33313, 26.148777999999997, -80.227624, 1378787), 4846: (33319, 26.181839000000004, -80.22759199999999, 687779), 4848: (33322, 26.150168, -80.273686, 971995), 4850: (33324, 26.110295, -80.270027, 748551), 4871: (33411, 26.715567999999998, -80.217416, 945804), 4883: (33433, 26.348386, -80.15787, 750611), 4900: (33463, 26.59398, -80.12772, 956985), 4901: (33467, 26.606929, -80.1777, 891289), 4917: (33511, 27.912173, -82.296703, 1043418), 4931: (33549, 28.123545, -82.449632, 804496), 4944: (33594, 27.916416, -82.249089, 845970), 4956: (33612, 28.05673, -82.451615, 977584), 4958: (33614, 28.007355, -82.51571, 947169), 4959: (33615, 28.009516, -82.585627, 806400), 4961: (33617, 28.036676, -82.39623, 997896), 4966: (33624, 28.076141, -82.523628, 732340), 5207: (34668, 28.303686, -82.70063, 991852), 5272: (30004, 34.122744, -84.296757, 983169), 5283: (30022, 34.029562, -84.240658, 895343), 5287: (30032, 33.735464, -84.266983, 1279515), 5289: (30034, 33.689216, -84.247271, 684856), 5293: (30040, 34.249703, -84.175246, 1042926), 5295: (30043, 34.009393, -84.001553, 1025648), 5296: (30044, 33.921718, -84.07267, 1647510), 5298: (30047, 33.874851, -84.113781, 981492), 5303: (30058, 33.727929, -84.123557, 991402), 5305: (30062, 33.999118, -84.467523, 1205424), 5306: (30064, 33.939798, -84.614184, 1004587), 5307: (30066, 34.036122, -84.505267, 1068058), 5308: (30067, 33.930563, -84.462218, 843881), 5313: (30075, 34.046659, -84.376691, 924280), 5314: (30076, 34.026099, -84.311677, 1007588), 5317: (30080, 33.872023, -84.507595, 854146), 5319: (30083, 33.789125, -84.199181, 1083646), 5324: (30093, 33.905579, -84.179966, 849655), 5326: (30096, 33.985868, -84.163754, 1023069), 5348: (30127, 33.883327, -84.688671, 974952), 5351: (30135, 33.696171, -84.742497, 843122), 5399: (30236, 33.511823, -84.316803, 672495), 5413: (30263, 33.393182, -84.823447, 845984), 5422: (30281, 33.553217, -84.213596, 838317), 5445: (30315, 33.708343, -84.38409, 985744), 5448: (30318, 33.78768, -84.443612, 1322975), 5456: (30331, 33.712646, -84.532291, 1091051), 5467: (30349, 33.614175, -84.497109, 1029558), 5624: (30721, 34.784599, -84.932948, 628397), 5671: (30906, 33.400357, -82.031397, 904689), 5672: (30907, 33.525, -82.10142, 1137325), 5797: (31419, 31.979874, -81.180758, 744045), 5871: (31707, 31.580916, -84.22168, 1026857), 5976: (31907, 32.477304, -84.903608, 857048), 6118: (83301, 42.44736, -114.5382, 958019), 6248: (83642, 43.609109, -116.398114, 1127613), 6345: (60004, 42.108547, -87.974705, 1303218), 6352: (60014, 42.23086, -88.326944, 1015514), 6354: (60016, 42.047152, -87.891674, 1000140), 6359: (60025, 42.078155, -87.817359, 929609), 6376: (60050, 42.347392000000006, -88.25975900000002, 796142), 6378: (60056, 42.068179, -87.932697, 1228572), 6381: (60062, 42.126945, -87.842535, 660497), 6383: (60067, 42.112431, -88.051211, 1190565), 6396: (60085, 42.360907, -87.862378, 1366729), 6399: (60089, 42.174011, -87.964322, 648602), 6408: (60102, 42.17082, -88.31874, 1101669), 6409: (60103, 41.966534, -88.165433, 1138305), 6419: (60115, 41.929327, -88.750764, 658961), 6422: (60120, 42.039135, -88.281994, 1117702), 6423: (60123, 42.040703, -88.311045, 1253425), 6424: (60126, 41.893914, -87.94058, 1001149), 6439: (60148, 41.869897, -88.011733, 816503), 6464: (60187, 41.857559, -88.112465, 1201687), 6465: (60188, 41.920273, -88.143298, 1001908), 6469: (60193, 42.012042, -88.090697, 1018655), 6470: (60194, 42.044152, -88.110153, 1029013), 6472: (60201, 42.057696, -87.696561, 967052), 6480: (60402, 41.838828, -87.791023, 1047469), 6486: (60411, 41.505061000000005, -87.606173, 995630), 6497: (60426, 41.604606, -87.66903, 887131), 6503: (60435, 41.55204, -88.11162, 858086), 6508: (60440, 41.704671, -88.075236, 1083221), 6509: (60441, 41.608015, -88.013188, 1004121), 6521: (60453, 41.713314, -87.756652, 1295469), 6544: (60477, 41.5674, -87.79266, 876657), 6552: (60504, 41.755826, -88.241597, 763771), 6553: (60505, 41.758169, -88.297124, 1252519), 6554: (60506, 41.762574, -88.353484, 958769), 6578: (60540, 41.774282, -88.147187, 724912), 6582: (60544, 41.618385, -88.199459, 1088511), 6601: (60565, 41.738696, -88.124239, 698757), 6609: (60608, 41.849103, -87.667335, 1388079), 6610: (60609, 41.812837, -87.654243, 1810407), 6611: (60610, 41.898992, -87.636455, 785322), 6614: (60613, 41.955735, -87.66121, 957378), 6615: (60614, 41.923621, -87.653367, 1249695), 6616: (60615, 41.800635, -87.604568, 954561), 6617: (60616, 41.844775, -87.626719, 1131679), 6618: (60617, 41.716207, -87.554349, 1689960), 6619: (60618, 41.944335, -87.702859, 2154276), 6620: (60619, 41.745767, -87.607643, 1824531), 6621: (60620, 41.742065, -87.655494, 1933641), 6622: (60621, 41.778204, -87.641571, 922536), 6623: (60622, 41.897111, -87.67088, 1486765), 6624: (60623, 41.846636, -87.71724, 2321022), 6625: (60624, 41.877445, -87.723846, 1109183), 6626: (60625, 41.968521, -87.703667, 1897491), 6627: (60626, 42.005107, -87.669133, 1031798), 6628: (60628, 41.69154, -87.62171, 1628626), 6629: (60629, 41.777493, -87.709271, 1828698), 6630: (60630, 41.971136, -87.757805, 1011982), 6632: (60632, 41.808605, -87.711782, 1384601), 6634: (60634, 41.944287, -87.811483, 1280838), 6635: (60636, 41.774317, -87.670123, 799788), 6636: (60637, 41.78128, -87.603401, 1273680), 6637: (60638, 41.781649, -87.774356, 895474), 6638: (60639, 41.918417, -87.755959, 1482971), 6639: (60640, 41.9726, -87.666715, 1282623), 6640: (60641, 41.944704, -87.745925, 1843511), 6641: (60643, 41.699379, -87.659992, 1102800), 6642: (60644, 41.881955, -87.757606, 1381237), 6643: (60645, 42.008098, -87.70603899999999, 803188), 6645: (60647, 41.918536, -87.698156, 1514517), 6646: (60649, 41.762027, -87.567858, 851854), 6647: (60651, 41.89987, -87.741859, 1681842), 6653: (60657, 41.940734, -87.654198, 1416448), 6655: (60660, 41.990183, -87.6648, 1018292), 6658: (60707, 41.923558, -87.816578, 830278), 6662: (60804, 41.843375, -87.763267, 1563111), 6819: (61265, 41.491529, -90.495895, 827955), 6996: (61554, 40.56042, -89.6091, 921561), 7059: (61761, 40.510903, -88.987912, 1010313), 7187: (62040, 38.761356, -90.096335, 1003725), 7304: (62301, 39.931262, -91.37972, 1124644), 7528: (62704, 39.7725, -89.68368, 782223), 7720: (46060, 40.040132, -86.00591, 635281), 7793: (46203, 39.743419, -86.104228, 978923), 7807: (46226, 39.836981, -86.046783, 884419), 7808: (46227, 39.674837, -86.127705, 1036873), 7831: (46307, 41.419705, -87.354291, 1174245), 7850: (46350, 41.614878, -86.734117, 805081), 7852: (46360, 41.709441000000005, -86.864786, 884135), 8012: (46901, 40.490485, -86.147278, 957746), 8125: (47150, 38.307855, -85.826843, 779293), 8208: (47374, 39.83393, -84.891208, 1138475), 8392: (47906, 40.495856, -86.96718, 1378157), 8651: (50317, 41.60277, -93.543515, 984423), 9088: (52001, 42.557520000000004, -90.69078, 839320), 9443: (66061, 38.884071, -94.870529, 704819), 9444: (66062, 38.840421, -94.78191, 1177756), 9828: (67212, 37.698135, -97.436018, 835751), 9868: (67401, 38.829855, -97.616195, 1199930), 10180: (40214, 38.158525, -85.786573, 1011097), 10256: (40475, 37.76341, -84.300058, 1115265), 10276: (40601, 38.199801, -84.947505, 897819), 10378: (41042, 38.986125, -84.648281, 785536), 10676: (42101, 37.018172, -86.458733, 752326), 10714: (42240, 36.868139, -87.479532, 607976), 10730: (42301, 37.747812, -87.178813, 951821), 10862: (70003, 29.9956, -90.214291, 760631), 10881: (70056, 29.890719, -90.030182, 843951), 10883: (70058, 29.878094, -90.069635, 671726), 10885: (70065, 30.024262, -90.249125, 932977), 10891: (70072, 29.85768, -90.13116, 1327350), 10909: (70115, 29.924584, -90.101956, 705027), 10911: (70117, 29.96924, -90.029607, 1073100), 10913: (70119, 29.974249, -90.087137, 853127), 10915: (70122, 30.005955, -90.065104, 1069001), 10919: (70126, 30.017111, -90.019351, 954040), 11037: (70560, 30.003568, -91.819418, 959065), 11039: (70570, 30.53255, -92.084616, 849509), 11516: (4401, 44.814135, -68.778574, 958961), 11856: (20743, 38.885663, -76.901034, 674663), 11857: (20744, 38.752955, -76.981503, 730889), 11861: (20748, 38.81605100000001, -76.93960600000001, 741492), 11881: (20783, 38.99934, -76.97502, 854125), 11902: (20854, 39.02874, -77.24094, 790307), 11911: (20874, 39.167973, -77.268161, 1219748), 11914: (20878, 39.105531, -77.24019, 1014497), 11922: (20902, 39.037324, -77.049792, 743260), 11924: (20904, 39.06504, -76.9815, 1159097), 11926: (20906, 39.081407000000006, -77.056897, 1155918), 11950: (21044, 39.212981, -76.882253, 723071), 11963: (21061, 39.164525, -76.634664, 873521), 11983: (21117, 39.428406, -76.769758, 807849), 11985: (21122, 39.127599, -76.512544, 1417253), 12009: (21206, 39.341591, -76.530778, 868362), 12010: (21207, 39.32382, -76.71426, 897695), 12018: (21215, 39.346278, -76.68128, 1157787), 12020: (21217, 39.307911, -76.637572, 754829), 12021: (21218, 39.325256, -76.605131, 1176664), 12024: (21221, 39.29484, -76.43652, 904667), 12025: (21222, 39.26302, -76.499604, 949595), 12027: (21224, 39.28068, -76.53798, 845730), 12031: (21228, 39.3279, -76.74396, 823393), 12032: (21229, 39.284902, -76.689882, 774127), 12035: (21234, 39.391101, -76.535369, 1472612), 12041: (21401, 39.002488, -76.510357, 1198354), 12045: (21502, 39.596959, -78.834511, 1064787), 12145: (21740, 39.643547, -77.718382, 1072001), 12275: (1085, 42.15636, -72.77874, 804841), 12294: (1201, 42.455451, -73.249993, 886893), 12358: (1453, 42.525279, -71.753473, 665383), 12463: (1841, 42.711749, -71.16384, 787327), 12465: (1844, 42.728753, -71.180274, 735085), 12482: (1902, 42.472369, -70.941341, 926201), 12503: (1960, 42.533241, -70.972639, 732783), 12506: (1970, 42.518116, -70.904469, 747207), 12549: (2124, 42.286139, -71.070555, 1010951), 12559: (2135, 42.35082, -71.11842, 833613), 12569: (2148, 42.43213, -71.056084, 1094427), 12572: (2151, 42.415223, -71.005325, 836478), 12574: (2155, 42.42132, -71.113443, 901256), 12576: (2169, 42.240464, -71.014144, 1147971), 12591: (2301, 42.090314, -71.038674, 932240), 12608: (2360, 41.87292, -70.64142, 1169486), 12696: (2703, 41.93916, -71.3028, 684670), 12710: (2740, 41.636223, -70.942002, 1074417), 12728: (2780, 41.904134, -71.10592, 831673), 12766: (48060, 42.9861, -82.46748, 821193), 12771: (48066, 42.503558, -82.936991, 833065), 12790: (48093, 42.516647, -83.007709, 1132198), 12795: (48098, 42.603558, -83.176258, 696411), 12797: (48103, 42.27078, -83.80866, 821426), 12798: (48104, 42.261244, -83.716523, 974928), 12811: (48126, 42.335197, -83.193476, 1120331), 12830: (48154, 42.397134, -83.377371, 627843), 12848: (48180, 42.234324, -83.269312, 1146551), 12850: (48183, 42.134388, -83.215861, 769075), 12852: (48185, 42.341489, -83.397113, 1038709), 12854: (48187, 42.331838, -83.477568, 986101), 12859: (48192, 42.197463, -83.185203, 969007), 12861: (48197, 42.233132, -83.623767, 877681), 12865: (48203, 42.424001, -83.101934, 1018253), 12866: (48204, 42.367514, -83.138488, 825862), 12867: (48205, 42.432798, -82.981462, 1510345), 12874: (48212, 42.408353, -83.058329, 1079865), 12875: (48213, 42.393275, -82.995296, 1018121), 12881: (48219, 42.423328, -83.250921, 1159163), 12883: (48221, 42.429028, -83.150684, 740263), 12885: (48224, 42.411143, -82.943461, 1349424), 12888: (48227, 42.389657, -83.193613, 1112949), 12889: (48228, 42.353376, -83.212913, 1229164), 12892: (48234, 42.430213, -83.042907, 850731), 12893: (48235, 42.425493, -83.19335, 1272138), 12896: (48238, 42.39504, -83.141885, 842395), 12906: (48310, 42.566407, -83.06801, 822610), 13018: (48601, 43.405416, -83.900719, 808508), 13071: (48706, 43.608032, -83.919043, 967997), 13131: (48823, 42.745357, -84.470605, 903248), 13146: (48843, 42.620869, -83.919104, 728142), 13159: (48858, 43.601402, -84.787107, 807096), 13193: (48911, 42.677285, -84.567592, 637601), 13198: (49001, 42.26388, -85.464, 952218), 13292: (49201, 42.248579, -84.384984, 1070591), 13296: (49221, 41.904241, -84.050711, 708848), 13406: (49423, 42.779463, -86.110617, 808509), 13407: (49424, 42.821709, -86.146908, 1008815), 13417: (49441, 43.168889, -86.263889, 760725), 13418: (49442, 43.233938, -86.169837, 795871), 13438: (49504, 42.986465, -85.721042, 808878), 13442: (49508, 42.873625, -85.625143, 928092), 13443: (49509, 42.88386, -85.70616, 939523), 13764: (55104, 44.955483, -93.160531, 978711), 13766: (55106, 44.957208, -93.052916, 1025487), 13771: (55112, 45.07938000000001, -93.1872, 695169), 13783: (55124, 44.74662, -93.20184, 759410), 13784: (55125, 44.90532, -92.92326, 625013), 13792: (55303, 45.261223, -93.440539, 938079), 13824: (55337, 44.770175, -93.281177, 1006668), 14017: (55901, 44.051928, -92.495114, 805608), 14870: (39401, 31.250639999999983, -89.27646000000003, 880189), 14997: (63017, 38.647818, -90.545814, 742994), 15000: (63021, 38.576504, -90.52892799999998, 1357300), 15003: (63026, 38.501758, -90.456792, 977150), 15006: (63031, 38.806089, -90.343437, 1131394), 15007: (63033, 38.794669, -90.277021, 1100165), 15056: (63116, 38.582028, -90.264153, 728502), 15063: (63123, 38.54388, -90.31842, 790258), 15069: (63129, 38.4644, -90.33203099999999, 1014263), 15076: (63136, 38.74358999999999, -90.261616, 1247729), 15086: (63301, 38.84742, -90.47699999999999, 942393), 15087: (63303, 38.7522, -90.53772, 723830), 15111: (63366, 38.83506, -90.74232000000002, 1207781), 15116: (63376, 38.78027, -90.62405, 1162331), 15722: (65203, 38.929931, -92.372948, 703292), 15998: (65807, 37.166766, -93.312621, 1166419), 16073: (59102, 45.785595, -108.576337, 934784), 16939: (89014, 36.063431, -115.054663, 1359953), 16940: (89015, 36.060266, -114.956815, 1322308), 16951: (89030, 36.210991, -115.128903, 1137729), 16963: (89101, 36.17496, -115.123394, 881585), 16965: (89103, 36.114166, -115.215839, 1004068), 16969: (89108, 36.205858, -115.225094, 1070872), 16970: (89109, 36.124358, -115.145079, 680848), 16971: (89110, 36.173684, -115.059521, 1169900), 16973: (89115, 36.229916, -115.07549, 1190053), 16974: (89117, 36.140602, -115.27402, 1014977), 16976: (89119, 36.086953, -115.137796, 1159390), 16978: (89121, 36.10451, -115.06771, 1499176), 16980: (89123, 36.023482, -115.150519, 1084817), 16982: (89128, 36.196444, -115.296213, 680993), 17045: (89502, 39.500666, -119.765124, 713221), 17048: (89509, 39.477902, -119.897581, 860620), 17304: (7002, 40.664207, -74.122276, 1143791), 17305: (7003, 40.805311, -74.187412, 798169), 17330: (7032, 40.76232, -74.12322, 758742), 17334: (7036, 40.635633, -74.256169, 716175), 17343: (7047, 40.793459, -74.022545, 1165428), 17345: (7052, 40.784909, -74.257646, 1023685), 17347: (7055, 40.859415, -74.130577, 1325391), 17351: (7060, 40.63134, -74.43702, 958403), 17372: (7083, 40.691867, -74.269598, 1024833), 17373: (7087, 40.770419, -74.030901, 1536081), 17377: (7093, 40.788201, -74.013854, 969695), 17382: (7104, 40.768591, -74.168632, 1258182), 17383: (7105, 40.72214, -74.140998, 666938), 17389: (7111, 40.72273, -74.232016, 950341), 17400: (7304, 40.718014, -74.075125, 684701), 17401: (7305, 40.69386, -74.07882, 1096291), 17402: (7306, 40.733605, -74.065616, 907735), 17403: (7307, 40.747679, -74.049894, 924526), 17440: (7470, 40.94725499999999, -74.245839, 1207079), 17455: (7601, 40.888613, -74.04776, 905325), 17491: (7675, 41.000621, -74.031463, 614430), 17507: (7726, 40.27776, -74.36112, 664991), 17509: (7728, 40.243519, -74.277392, 1165604), 17590: (7960, 40.79368, -74.491343, 892876), 17615: (8021, 39.80981500000001, -75.001119, 807447), 17642: (8053, 39.888912, -74.91159900000001, 816034), 17643: (8054, 39.946438, -74.915955, 882160), 17668: (8081, 39.773333, -75.006667, 1038478), 17721: (8302, 39.438881, -75.22817499999998, 745786), 17754: (8401, 39.362143, -74.437879, 635237), 17769: (8527, 40.10682, -74.34102, 1042944), 17776: (8540, 40.36746, -74.66952, 1029873), 17804: (8701, 40.084328, -74.203837, 1503686), 17809: (8724, 40.086348, -74.118215, 988757), 17824: (8753, 39.98868, -74.17956, 958976), 17837: (8816, 40.429733, -74.407288, 797374), 17838: (8817, 40.51467, -74.395296, 1055659), 17862: (8854, 40.552711, -74.458211, 946182), 17866: (8861, 40.519012, -74.27612, 803710), 17872: (8873, 40.49934, -74.52138, 719249), 17873: (8876, 40.54374, -74.66004, 692439), 17881: (8901, 40.48799, -74.447033, 788813), 17947: (87105, 35.043217, -106.694148, 1021877), 17951: (87109, 35.156553, -106.565192, 869414), 17953: (87111, 35.134826, -106.518962, 924148), 17954: (87112, 35.098578, -106.513879, 903443), 17959: (87120, 35.141221, -106.704928, 820578), 17963: (87124, 35.2566, -106.69656, 1229672), 18000: (87501, 35.6997, -105.96720000000003, 943826), 18001: (87505, 35.621141, -105.967103, 1639948), 18111: (88005, 32.323217, -106.805117, 858061), 18148: (88101, 34.40538, -103.24842, 831848), 18166: (88201, 33.393099, -104.522917, 807529), 18189: (88310, 32.899416, -105.951065, 647087), 18239: (10002, 40.715523, -73.988379, 1804934), 18240: (10003, 40.732373, -73.989477, 916756), 18245: (10009, 40.724608, -73.980332, 1049990), 18247: (10011, 40.74179, -73.999332, 991368), 18251: (10016, 40.745154, -73.980751, 1199504), 18256: (10021, 40.768479, -73.960718, 1994083), 18258: (10023, 40.777277, -73.982489, 1223444), 18259: (10024, 40.786538, -73.978644, 1458475), 18260: (10025, 40.799621, -73.970312, 2077993), 18262: (10027, 40.81207, -73.95437700000001, 1100869), 18263: (10028, 40.778345, -73.955085, 769340), 18264: (10029, 40.790284, -73.946781, 1376140), 18266: (10031, 40.827379, -73.948071, 1074366), 18267: (10032, 40.83668, -73.939944, 1207203), 18268: (10033, 40.847553, -73.936012, 1086762), 18269: (10034, 40.867888, -73.919847, 632116), 18275: (10040, 40.85837, -73.927473, 758967), 18285: (10128, 40.779563, -73.949559, 975740), 18308: (10306, 40.566903, -74.120829, 965567), 18313: (10312, 40.542579, -74.178991, 1066263), 18314: (10314, 40.606393, -74.152402, 1410665), 18315: (10451, 40.820195, -73.920218, 770964), 18316: (10452, 40.841676, -73.921773, 1128359), 18317: (10453, 40.852613, -73.914221, 1613463), 18320: (10456, 40.830175, -73.906791, 1621298), 18321: (10457, 40.846394, -73.902732, 1252287), 18322: (10458, 40.859035, -73.890784, 1714912), 18324: (10460, 40.837082, -73.880734, 1045006), 18325: (10461, 40.844984, -73.843255, 793453), 18326: (10462, 40.840999, -73.85721, 1583652), 18327: (10463, 40.881512, -73.907521, 1052130), 18329: (10465, 40.823241, -73.826218, 1032712), 18330: (10466, 40.889675, -73.845608, 1158697), 18331: (10467, 40.873256, -73.870576, 1636915), 18332: (10468, 40.868013, -73.896417, 1343660), 18333: (10469, 40.868747, -73.849303, 1316797), 18336: (10472, 40.830485, -73.870026, 1592547), 18337: (10473, 40.818719, -73.85718, 902598), 18403: (10701, 40.941652, -73.877562, 1120600), 18432: (10940, 41.4744, -74.41098, 705725), 18451: (10977, 41.12021099999999, -74.046736, 855664), 18466: (11003, 40.699109, -73.703659, 770038), 18481: (11103, 40.762281, -73.910107, 1025971), 18483: (11105, 40.778285, -73.910175, 719347), 18484: (11106, 40.761688, -73.930747, 663520), 18485: (11201, 40.695472, -73.992723, 1086794), 18486: (11203, 40.649673, -73.937666, 1306769), 18487: (11204, 40.620189, -73.985706, 1739806), 18489: (11206, 40.703008, -73.943208, 1721909), 18490: (11207, 40.669311, -73.895528, 1325520), 18491: (11208, 40.673964, -73.872964, 1441614), 18492: (11209, 40.623738, -74.033806, 1070493), 18493: (11210, 40.628777, -73.945814, 1512513), 18494: (11211, 40.714112, -73.952354, 1850931), 18495: (11212, 40.663426, -73.912354, 2091749), 18496: (11213, 40.671767, -73.935934, 1235068), 18497: (11214, 40.59848, -73.996892, 1260932), 18498: (11215, 40.666364, -73.985457, 1083935), 18499: (11216, 40.679695, -73.950292, 1388093), 18501: (11218, 40.641581, -73.975901, 1177436), 18502: (11219, 40.631209, -73.998416, 2011062), 18503: (11220, 40.642875, -74.015564, 1637759), 18504: (11221, 40.693561, -73.926509, 1545615), 18506: (11223, 40.59646, -73.972916, 1680607), 18507: (11224, 40.577387, -73.994493, 914559), 18508: (11225, 40.662208, -73.95527, 972439), 18509: (11226, 40.647083, -73.954915, 1652182), 18510: (11228, 40.620567, -74.015141, 728989), 18511: (11229, 40.598356, -73.939325, 1788633), 18512: (11230, 40.619153, -73.965619, 1345012), 18515: (11233, 40.671472, -73.924489, 1405277), 18516: (11234, 40.619061, -73.923116, 1728856), 18517: (11235, 40.582828, -73.951811, 1331287), 18518: (11236, 40.640108, -73.904411, 2112599), 18519: (11237, 40.704643, -73.921609, 1036618), 18520: (11238, 40.678989, -73.961819, 1014648), 18522: (11354, 40.770167, -73.825967, 857303), 18523: (11355, 40.754005, -73.821132, 2012990), 18532: (11365, 40.738549, -73.790001, 833273), 18535: (11368, 40.752572, -73.854759, 2445082), 18537: (11370, 40.760333, -73.890833, 744776), 18539: (11372, 40.749542, -73.883319, 1741068), 18540: (11373, 40.738937, -73.87916, 2411446), 18541: (11374, 40.727079, -73.861454, 919603), 18542: (11375, 40.721216, -73.85021, 1084801), 18543: (11377, 40.743107, -73.906134, 2099839), 18546: (11385, 40.70286, -73.87974, 2163048), 18555: (11419, 40.688921, -73.823304, 912710), 18556: (11420, 40.674361, -73.813156, 986166), 18565: (11432, 40.715744, -73.794362, 936949), 18567: (11434, 40.67704700000001, -73.778208, 1238432), 18568: (11435, 40.699477, -73.808819, 1312198), 18577: (11520, 40.652023, -73.588242, 930166), 18583: (11550, 40.708785, -73.624573, 1039025), 18605: (11590, 40.757311, -73.577498, 655179), 18608: (11691, 40.602157, -73.760226, 1234808), 18616: (11704, 40.709193, -73.371464, 894840), 18618: (11706, 40.63611100000001, -73.197222, 1263523), 18625: (11717, 40.78092, -73.25454, 1276649), 18645: (11743, 40.869083, -73.40930000000002, 689325), 18646: (11746, 40.817398, -73.369148, 1187837), 18653: (11756, 40.726315, -73.517312, 722672), 18654: (11757, 40.688951, -73.376317, 927780), 18655: (11758, 40.686884, -73.469397, 1317528), 18666: (11772, 40.77504, -72.89574, 930298), 18837: (12180, 42.74400000000001, -73.60511999999999, 998522), 18974: (12550, 41.51748, -74.06022, 939905), 18999: (12601, 41.701664, -73.916805, 672133), 19000: (12603, 41.69706, -73.8624, 692542), 19174: (13021, 42.920643999999996, -76.559964, 1023992), 19342: (13440, 43.21386, -75.45954000000003, 731885), 19455: (13760, 42.141, -76.07526, 686758), 19555: (14075, 42.733234, -78.834422, 803839), 19564: (14094, 43.1649, -78.70248, 817142), 19573: (14120, 43.07124, -78.81414, 680260), 19586: (14150, 43.001575, -78.861741, 1057553), 19605: (14215, 42.933454000000005, -78.81184, 822574), 19611: (14221, 42.980183, -78.734894, 1025466), 19614: (14224, 42.841518, -78.761265, 648642), 19641: (14450, 43.087492, -77.432058, 630498), 19702: (14580, 43.220645, -77.464013, 963947), 19713: (14609, 43.174537, -77.559782, 774411), 19731: (14701, 42.094174, -79.251081, 745693), 19819: (14850, 42.445573, -76.496428, 1108149), 19893: (27105, 36.150762, -80.234242, 1014466), 19899: (27203, 35.65104, -79.83162, 1181449), 19929: (27284, 36.11629, -80.092145, 808530), 19951: (27330, 35.45927699999999, -79.16861100000001, 1283279), 19962: (27360, 35.880803, -80.083016, 935399), 19970: (27405, 36.11058, -79.74059999999999, 907458), 19971: (27406, 36.021374, -79.767916, 1203637), 19972: (27407, 36.01266, -79.86996, 808375), 19975: (27410, 36.09839499999999, -79.885035, 874578), 19978: (27502, 35.711653, -78.81965, 862484), 19987: (27511, 35.758852, -78.780766, 958627), 19989: (27514, 35.934949, -79.037474, 1225225), 20039: (27606, 35.754707, -78.722559, 975621), 20043: (27610, 35.761643, -78.583787, 797178), 20047: (27615, 35.889314, -78.637839, 889969), 20052: (27705, 36.017812, -78.948419, 902474), 20054: (27707, 35.964557, -78.940527, 844388), 20085: (27834, 35.62638, -77.43858, 905273), 20104: (27858, 35.589407, -77.351275, 866861), 20132: (27893, 35.73252, -77.920181, 929840), 20203: (28025, 35.400953, -80.583807, 737489), 20280: (28205, 35.220088, -80.790126, 733720), 20285: (28210, 35.133058, -80.859674, 839483), 20290: (28215, 35.239821, -80.725177, 968604), 20297: (28269, 35.314436, -80.805053, 916021), 20309: (28314, 35.05772, -79.003491, 1116167), 20453: (28540, 34.764003, -77.434331, 683445), 20485: (28601, 35.75358, -81.3249, 778963), 20520: (28645, 35.949000000000005, -81.52980000000001, 870961), 20526: (28655, 35.74403999999999, -81.71316, 1152146), 20698: (58103, 46.852, -96.814801, 875835), 20868: (58501, 46.819042, -100.780969, 1071623), 21042: (43026, 40.032483, -83.135808, 821600), 21057: (43055, 40.116667, -82.433333, 1303661), 21066: (43068, 39.962571, -82.783851, 827768), 21075: (43081, 40.110098, -82.907426, 806772), 21093: (43123, 39.881816, -83.091047, 797666), 21098: (43130, 39.70728, -82.60788, 1146283), 21127: (43204, 39.955851, -83.082221, 932157), 21130: (43207, 39.89394, -82.95408, 683479), 21144: (43224, 40.040081, -82.966132, 684788), 21146: (43228, 39.951399, -83.128, 803544), 21147: (43229, 40.083167, -82.975693, 727800), 21148: (43230, 40.044616, -82.856435, 796781), 21153: (43302, 40.588875, -83.12552, 937892), 21293: (43701, 39.95424, -81.98496, 1219094), 21426: (44035, 41.370813, -82.114096, 1262626), 21442: (44060, 41.72262, -81.35652, 1252034), 21451: (44077, 41.75, -81.283333, 1081943), 21466: (44102, 41.470294, -81.737685, 1095903), 21469: (44105, 41.45247899999999, -81.625585, 1166085), 21471: (44107, 41.482343, -81.794563, 1413672), 21473: (44109, 41.450419, -81.7019, 742016), 21475: (44111, 41.459888, -81.784804, 998883), 21482: (44118, 41.498765999999996, -81.55459399999998, 911896), 21484: (44120, 41.472129, -81.578028, 771489), 21488: (44124, 41.49828, -81.64374, 866186), 21494: (44130, 41.380101, -81.78571899999999, 1082876), 21498: (44134, 41.387185, -81.702198, 997187), 21500: (44136, 41.31288, -81.83472, 1006952), 21514: (44203, 41.014711, -81.6145, 995843), 21537: (44256, 41.134844, -81.860472, 801455), 21662: (44646, 40.802818, -81.520846, 932102), 21691: (44691, 40.806978, -81.956817, 948436), 21757: (44870, 41.40498, -82.73142, 976687), 21777: (45011, 39.406984, -84.509883, 1158450), 21778: (45013, 39.408216, -84.617598, 802150), 21779: (45014, 39.33444, -84.56226, 791131), 21790: (45044, 39.484738, -84.383452, 1057298), 21802: (45069, 39.34146, -84.398674, 799889), 21824: (45140, 39.267042, -84.292122, 866424), 21874: (45231, 39.244265, -84.540628, 730239), 21879: (45238, 39.110911, -84.613884, 819956), 21983: (45424, 39.84564, -84.11172, 1207057), 22002: (45601, 39.328095, -82.982598, 1209311), 22132: (45840, 41.043063, -83.643019, 1215961), 22261: (73099, 35.496256, -97.732383, 765351), 22298: (73160, 35.38116, -97.47588, 722801), 22339: (73505, 34.616916, -98.457365, 913264), 22508: (74012, 36.04503, -95.808242, 1055667), 22841: (97006, 45.516558, -122.858874, 975705), 22842: (97007, 45.472666, -122.856983, 1164208), 22874: (97045, 45.340277, -122.560941, 780143), 22941: (97206, 45.487218, -122.598613, 1086783), 22956: (97223, 45.43889, -122.772276, 797153), 22960: (97229, 45.540884, -122.82998, 904203), 22968: (97301, 44.928656, -122.960707, 1323562), 22970: (97303, 45.01182, -123.01566, 1220579), 22974: (97321, 44.6256, -123.06642, 804702), 22980: (97330, 44.603787, -123.273273, 879908), 23025: (97402, 44.057393, -123.188424, 891151), 23028: (97405, 43.94946, -123.12804, 1034416), 23081: (97470, 43.223282, -123.36627, 764984), 23104: (97504, 42.335443, -122.837108, 616990), 23147: (97701, 44.098205, -121.288771, 992832), 23298: (15068, 40.576451, -79.72398, 656512), 23376: (15237, 40.549733, -80.039957, 837785), 23381: (15301, 40.175267, -80.251514, 1127859), 23529: (15601, 40.29676, -79.542457, 1099708), 23556: (15642, 40.328956, -79.721348, 774652), 23718: (16001, 40.858537, -79.902516, 1033261), 24001: (16801, 40.796516, -77.844795, 808772), 24094: (17013, 40.203056, -77.313611, 1300461), 24129: (17055, 40.21923700000001, -77.00104699999999, 1164678), 24174: (17201, 39.933480000000024, -77.67455999999997, 972709), 24235: (17331, 39.79661999999999, -77.00142000000002, 989022), 24259: (17402, 39.97683, -76.68531299999998, 986673), 24260: (17403, 39.950251, -76.71045600000001, 1037990), 24261: (17404, 39.971839, -76.774584, 1166949), 24305: (17601, 40.0614, -76.32204, 1032808), 24306: (17602, 40.02925, -76.265633, 1033718), 24307: (17603, 40.04586799999999, -76.354179, 1159919), 24308: (17701, 41.267399999999995, -77.03507999999998, 1040087), 24498: (18102, 40.604201, -75.481145, 976022), 24499: (18103, 40.592173, -75.475434, 1313618), 24500: (18104, 40.603189, -75.532165, 837862), 24668: (18702, 41.234843000000005, -75.87731299999999, 843031), 24711: (18901, 40.332324, -75.116759, 798969), 24756: (19020, 40.102797, -74.929344, 1106311), 24788: (19067, 40.2024, -74.83098, 1148875), 24809: (19104, 39.963766, -75.198203, 773985), 24813: (19111, 40.057937, -75.081966, 927549), 24821: (19120, 40.036043, -75.119434, 1116623), 24825: (19124, 40.013115, -75.094734, 1542667), 24832: (19131, 39.978878, -75.220604, 836781), 24833: (19132, 39.992702, -75.166366, 1011368), 24835: (19134, 39.994605, -75.113258, 1072114), 24837: (19136, 40.044445, -75.024762, 789132), 24840: (19139, 39.962447, -75.230101, 722724), 24841: (19140, 40.013413, -75.144023, 899102), 24844: (19143, 39.943711, -75.229131, 1583277), 24845: (19144, 40.031925, -75.173958, 1160288), 24846: (19145, 39.924229, -75.186845, 990055), 24849: (19148, 39.922429, -75.158025, 879169), 24850: (19149, 40.038521, -75.067175, 738501), 24863: (19320, 39.984474999999996, -75.81097799999999, 737204), 24866: (19335, 40.0165, -75.713718, 928532), 24885: (19380, 39.982089, -75.603385, 927407), 24886: (19382, 39.942544, -75.597966, 904908), 24889: (19403, 40.147771, -75.375422, 853534), 24903: (19446, 40.235193, -75.289081, 1199840), 24909: (19464, 40.24236, -75.63666, 956621), 24999: (2860, 41.872972, -71.39274, 853259), 25019: (2895, 42.0039, -71.502576, 911135), 25028: (2909, 41.820105, -71.45187, 677885), 25137: (29203, 34.098180000000006, -81.03618000000003, 785827), 25145: (29223, 34.08846, -80.92287, 787988), 25208: (29445, 33.02808, -80.04732, 733329), 25233: (29483, 33.017824, -80.21135, 801747), 25371: (29720, 34.709391, -80.775133, 902823), 25377: (29730, 34.929113, -81.022958, 965576), 25828: (37013, 36.037491, -86.638596, 1204900), 25851: (37042, 36.56214, -87.40572, 1229204), 25874: (37075, 36.316241, -86.607771, 1048244), 25898: (37130, 35.870529, -86.341561, 1009946), 25946: (37211, 36.075248, -86.7207, 1217617), 26047: (37421, 35.02529, -85.144734, 644709), 26066: (37660, 36.548955, -82.546424, 838781), 26197: (37922, 35.85642, -84.12834, 750155), 26212: (38018, 35.13832, -89.758273, 890202), 26253: (38109, 35.046864, -90.06820499999999, 919908), 26254: (38111, 35.112624, -89.94683200000001, 799387), 26257: (38115, 35.045523, -89.849029, 1008081), 26258: (38116, 35.036558, -90.00901, 840297), 26260: (38118, 35.048583, -89.92596099999999, 899000), 26266: (38127, 35.240147, -90.020802, 1225352), 26267: (38128, 35.219361, -89.925899, 912466), 26271: (38134, 35.19186, -89.92536, 700518), 26304: (38301, 35.610381, -88.819872, 877424), 26305: (38305, 35.681229, -88.821998, 628565), 26363: (38401, 35.609931, -87.048941, 1159889), 26441: (75006, 32.961351, -96.891307, 966042), 26442: (75007, 33.006252, -96.8866, 865925), 26450: (75023, 33.057653, -96.737455, 1083919), 26459: (75040, 32.925157, -96.622452, 1276217), 26462: (75043, 32.857549, -96.597118, 903870), 26467: (75052, 32.679596, -97.013708, 1333908), 26471: (75060, 32.798903, -96.950146, 925469), 26472: (75061, 32.824483, -96.953242, 801059), 26473: (75062, 32.846175, -96.963386, 723228), 26476: (75067, 33.077549, -97.04926, 805596), 26485: (75080, 32.963287, -96.745163, 1006554), 26493: (75093, 33.032072, -96.802811, 866607), 26524: (75149, 32.770243, -96.613013, 1321983), 26525: (75150, 32.814395, -96.625303, 1026917), 26556: (75211, 32.81622, -96.88866, 1465859), 26560: (75216, 32.707957, -96.787266, 1013836), 26561: (75217, 32.72015, -96.676927, 1230642), 26564: (75220, 32.863782, -96.873944, 1251146), 26569: (75227, 32.766974, -96.683948, 1123501), 26570: (75228, 32.825581, -96.681423, 1499432), 26573: (75231, 32.876553, -96.751035, 1161150), 26581: (75240, 32.931962, -96.789191, 984463), 26583: (75243, 32.911604, -96.732266, 1163405), 26593: (75287, 33.000097, -96.842497, 893096), 26837: (76010, 32.722794, -97.084692, 1181255), 26844: (76017, 32.656676, -97.160065, 691672), 26863: (76051, 32.933618, -97.097514, 658397), 26893: (76106, 32.799177, -97.358089, 1065556), 26902: (76116, 32.714361, -97.464571, 853722), 26905: (76119, 32.6805, -97.26498, 623984), 26912: (76133, 32.652107, -97.377051, 950941), 26921: (76180, 32.861011, -97.21613, 1003133), 26922: (76201, 33.220863, -97.144294, 1160675), 27212: (77009, 29.796922, -95.368503, 686228), 27218: (77015, 29.770126, -95.173187, 1168180), 27239: (77036, 29.701008, -95.536659, 1279591), 27257: (77055, 29.797867, -95.497137, 781083), 27274: (77072, 29.697439, -95.587015, 1166457), 27279: (77077, 29.750197, -95.611073, 988002), 27282: (77080, 29.81684, -95.522482, 716128), 27283: (77081, 29.713931, -95.479494, 1130813), 27285: (77083, 29.690885, -95.651136, 1192974), 27286: (77084, 29.82114, -95.640017, 1390136), 27290: (77088, 29.880263, -95.453243, 841532), 27295: (77093, 29.86261, -95.339011, 1107331), 27300: (77099, 29.670332, -95.586361, 732528), 27344: (77379, 30.027227, -95.529294, 850962), 27366: (77429, 29.991106, -95.669038, 861843), 27383: (77450, 29.768276, -95.743065, 830117), 27398: (77469, 29.590019, -95.752785, 675869), 27406: (77478, 29.627645, -95.635597, 1192124), 27407: (77479, 29.576266, -95.629289, 1106336), 27426: (77511, 29.4, -95.23944, 849400), 27432: (77520, 29.772539999999996, -94.94484000000001, 794129), 27460: (77573, 29.503872, -95.092521, 716135), 27523: (77840, 30.603583, -96.311081, 848416), 27545: (77901, 28.70675, -97.18143, 771678), 27602: (78040, 27.512693, -99.488193, 869528), 27606: (78046, 27.43465, -99.473074, 715659), 27646: (78130, 29.719620000000003, -98.0808, 928297), 27667: (78201, 29.46724, -98.530042, 1055189), 27672: (78207, 29.421586, -98.523179, 1069230), 27674: (78209, 29.484722, -98.465556, 816407), 27688: (78223, 29.321261, -98.409516, 685467), 27692: (78227, 29.41514, -98.635627, 938334), 27693: (78228, 29.459623, -98.574755, 1123567), 27705: (78240, 29.49858, -98.60574, 693305), 27712: (78250, 29.50803, -98.664842, 1272810), 27786: (78501, 26.21359, -98.235546, 1065379), 27790: (78520, 25.98174, -97.53534, 939927), 27791: (78521, 25.939204, -97.447349, 1284472), 27795: (78539, 26.33202, -98.16384, 1485569), 27801: (78550, 26.194287, -97.686999, 1130641), 27813: (78572, 26.214660000000002, -98.35163999999999, 1985628), 27816: (78577, 26.18745, -98.183954, 1180830), 27823: (78586, 26.185620000000004, -97.66463999999998, 781559), 27830: (78596, 26.160167, -97.98636, 1222630), 27884: (78664, 30.512352000000003, -97.670283, 1085353), 27885: (78666, 29.882645, -97.945088, 951371), 27896: (78704, 30.244144, -97.76286, 1015894), 27919: (78741, 30.234123, -97.718296, 996261), 27922: (78745, 30.208076, -97.800448, 819599), 27930: (78753, 30.371378, -97.671747, 746880), 27934: (78758, 30.378845, -97.711093, 830301), 27935: (78759, 30.3972, -97.75176, 749110), 27948: (78840, 29.367307999999998, -100.890893, 741186), 27951: (78852, 28.715762, -100.492839, 1111283), 28061: (79109, 35.164304, -101.888752, 1003911), 28290: (79907, 31.711168, -106.331389, 1188336), 28292: (79912, 31.842644, -106.540333, 1338218), 28293: (79915, 31.751969, -106.381303, 646509), 28295: (79924, 31.899322, -106.414327, 980263), 28296: (79925, 31.77928, -106.365646, 1009553), 28297: (79927, 31.65522, -106.22826000000002, 812142), 28302: (79936, 31.786132, -106.260892, 1889084), 28310: (84010, 40.871662, -111.89048599999998, 1025568), 28313: (84015, 41.119274, -112.02864699999999, 687090), 28372: (84084, 40.618542, -111.967531, 913910), 28398: (84118, 40.654603, -111.98403399999998, 1022181), 28399: (84119, 40.69207899999999, -111.94783200000005, 1123443), 28400: (84120, 40.69656, -112.01747999999999, 1085189), 28401: (84121, 40.622100999999994, -111.82423999999999, 687838), 28445: (84404, 41.276379000000006, -111.987441, 695436), 28475: (84604, 40.264063, -111.623041, 1199527), 28885: (22003, 38.828264, -77.212338, 938259), 28886: (22015, 38.790084, -77.280669, 661795), 28915: (22191, 38.626232, -77.274322, 619578), 28916: (22192, 38.68001, -77.309022, 1065637), 28917: (22193, 38.646162, -77.349693, 1252986), 28921: (22204, 38.859707, -77.095607, 837190), 28931: (22304, 38.817208, -77.122599, 673561), 28945: (22407, 38.28227900000001, -77.557232, 911314), 28982: (22554, 38.460218, -77.437061, 1134999), 29219: (23223, 37.558121, -77.374277, 977889), 29228: (23233, 37.62284, -77.613493, 1003424), 29246: (23320, 36.7434, -76.22574, 687106), 29248: (23322, 36.579718, -76.307527, 1209539), 29282: (23434, 36.731942, -76.60187, 656478), 29290: (23451, 36.86373, -76.012395, 994509), 29291: (23452, 36.839129, -76.090953, 1179088), 29292: (23454, 36.837731, -76.025953, 1085555), 29293: (23455, 36.888297, -76.144677, 978704), 29294: (23456, 36.775899, -76.075614, 1894045), 29298: (23462, 36.839595, -76.151374, 1289292), 29299: (23464, 36.798333, -76.177537, 1430487), 29304: (23503, 36.945923, -76.253486, 834031), 29317: (23602, 37.124608, -76.519972, 982544), 29323: (23608, 37.143493, -76.539049, 670573), 29330: (23666, 37.049912, -76.412922, 1121091), 29331: (23669, 37.041146, -76.337539, 932694), 29344: (23803, 37.21386, -77.45568, 688932), 29445: (24060, 37.229033, -80.414886, 1109648), 29724: (98003, 47.30994, -122.3139, 1012670), 29738: (98023, 47.30448, -122.37258, 862166), 29745: (98031, 47.386336, -122.195858, 1312379), 29748: (98034, 47.718053, -122.198946, 714043), 29750: (98037, 47.851103, -122.281511, 916636), 29759: (98052, 47.683648, -122.121837, 1166435), 29772: (98103, 47.671009, -122.340102, 985933), 29781: (98115, 47.683440999999995, -122.291533, 723892), 29784: (98118, 47.541963, -122.267649, 838632), 29790: (98133, 47.73966, -122.33334, 994085), 29811: (98208, 47.894914, -122.193377, 852798), 29817: (98225, 48.746494, -122.493289, 685105), 29818: (98226, 48.763344999999994, -122.443649, 1031399), 29929: (98390, 47.17926, -122.19204, 1059991), 30039: (98632, 46.157629, -122.985831, 717598), 30066: (98682, 45.671798, -122.511245, 654119), 30116: (98902, 46.595168, -120.537142, 739927), 30238: (99205, 47.69545, -117.442334, 946230), 30248: (99301, 46.286919, -119.092773, 955511), 30260: (99336, 46.19472, -119.13324, 613656), 30545: (25401, 39.461266, -77.965102, 979620), 30733: (26003, 40.069414, -80.687797, 1078181), 30756: (26101, 39.263058, -81.53612, 883681), 30921: (26554, 39.476203, -80.152059, 838608), 31079: (53081, 43.741822, -87.728355, 861522), 31149: (53204, 43.017316, -87.924759, 1018678), 31154: (53209, 43.12592, -87.946764, 850514), 31160: (53215, 42.997687000000006, -87.942662, 1340543), 31163: (53218, 43.113642, -87.991022, 733334), 31189: (53511, 42.5589, -89.08734, 860379), 31215: (53545, 42.689826, -89.050644, 649016), 31259: (53704, 43.117217, -89.335082, 883146), 31262: (53711, 43.030573, -89.444075, 893706), 31430: (54220, 44.095713, -87.71106, 860026), 31568: (54601, 43.795836, -91.221089, 899352), 31751: (54935, 43.775242, -88.431561, 1159375)}
    
    # Distances
    #(warehouse, customer): distance
    distance = {(1, 109): 1105.4079616149575, (1, 872): 2540.994028099361, (1, 873): 2548.940660874155, (1, 877): 2545.639130531614, (1, 879): 2546.786689576338, (1, 884): 2538.082904014493, (1, 889): 2543.2161528592183, (1, 891): 2535.5403452836626, (1, 892): 2553.013203507224, (1, 894): 2552.1413473001094, (1, 896): 2545.0152859238697, (1, 903): 2545.5703340772025, (1, 909): 2533.0900742888275, (1, 910): 2536.5681323514727, (1, 912): 2531.2412746867203, (1, 913): 2525.2633939782836, (1, 916): 2523.164069235336, (1, 926): 2539.562764756633, (1, 927): 2536.958932383371, (1, 948): 2532.712145215077, (1, 961): 2538.587726874551, (1, 962): 2539.696340333073, (1, 963): 2540.875595698757, (1, 967): 2549.0607527941797, (1, 974): 2544.043326758229, (1, 998): 2551.9399484103733, (1, 1014): 2729.542149325368, (1, 1086): 2529.5000144065366, (1, 1087): 2529.3900615651933, (1, 1089): 2521.5471040531957, (1, 1090): 2524.8435294599362, (1, 1092): 2536.3636147911798, (1, 1097): 2527.399467327762, (1, 1107): 2542.6648911365664, (1, 1387): 1329.7765111302372, (1, 1554): 1202.4426778555114, (1, 1827): 2895.72566617415, (1, 1828): 2896.758079396525, (1, 1829): 2897.8462543659402, (1, 1830): 2895.693837471597, (1, 1831): 2896.565473317086, (1, 1832): 2895.798159086166, (1, 1833): 2896.0478307116837, (1, 1836): 2895.306035819451, (1, 1841): 2900.164265232794, (1, 1843): 2898.0342306388793, (1, 1844): 2898.8298279234214, (1, 1845): 2896.159478700459, (1, 1847): 2888.4009826732, (1, 1848): 2891.1726209881754, (1, 1849): 2904.0088841290894, (1, 1850): 2905.5114741443685, (1, 1851): 2892.884941611159, (1, 1852): 2892.733792784502, (1, 1854): 2894.342012435311, (1, 1856): 2887.5383615018086, (1, 1857): 2890.7900662798857, (1, 1858): 2902.992361918146, (1, 1861): 2897.3663484841168, (1, 1866): 2887.054460927836, (1, 1867): 2900.6101359718245, (1, 1868): 2899.188993143569, (1, 1870): 2898.1370874917184, (1, 1871): 2900.5213364002216, (1, 1875): 2894.4406080624385, (1, 1880): 2889.5970370063546, (1, 1882): 2889.913872719584, (1, 1883): 2906.023451529368, (1, 1889): 2891.6457321332987, (1, 1893): 2898.5744870196804, (1, 1894): 2896.6837220366597, (1, 1899): 2890.131369310059, (1, 1900): 2891.718019161322, (1, 1902): 2902.0283422353705, (1, 1905): 2904.3657033981763, (1, 1907): 2893.4406944337766, (1, 1910): 2894.822029983213, (1, 1917): 2910.9152035324205, (1, 1920): 2893.9432779662156, (1, 1935): 2905.39162293927, (1, 1937): 2907.465066097206, (1, 1946): 2886.495373637642, (1, 1949): 2889.1326418085937, (1, 1950): 2879.6150925013158, (1, 1951): 2884.0170634168453, (1, 1952): 2886.2413740607167, (1, 1953): 2888.4296638124006, (1, 1954): 2885.85559638291, (1, 1958): 2888.059636126254, (1, 1960): 2892.0216118190865, (1, 1968): 2893.5870041598114, (1, 1969): 2906.568594163402, (1, 1974): 2903.1139506807726, (1, 1975): 2902.857166682085, (1, 1979): 2897.3205236963545, (1, 1980): 2896.1872523010106, (1, 1981): 2898.3519324580902, (1, 1985): 2899.975226296766, (1, 1994): 2874.7022940891457, (1, 2011): 2889.577735362382, (1, 2019): 2909.4396343151825, (1, 2020): 2906.808497455017, (1, 2029): 2896.157031628483, (1, 2030): 2904.99534665244, (1, 2032): 2894.0733173270446, (1, 2033): 2900.0658909595063, (1, 2034): 2899.633774245524, (1, 2036): 2887.7026187072374, (1, 2037): 2890.811288710335, (1, 2038): 2893.2917424341003, (1, 2042): 2924.6975227372423, (1, 2050): 2899.136912095434, (1, 2051): 2898.3239677986526, (1, 2053): 2899.315759025759, (1, 2054): 2902.0825433571977, (1, 2066): 2896.388778340808, (1, 2067): 2896.590855067609, (1, 2071): 2869.630022321818, (1, 2072): 2875.121912952273, (1, 2073): 2861.647916903062, (1, 2074): 2860.718785768958, (1, 2080): 2851.3167200187318, (1, 2082): 2878.0050567896087, (1, 2083): 2880.8660671643256, (1, 2089): 2875.349642688338, (1, 2090): 2878.076802011852, (1, 2092): 2874.809182276202, (1, 2098): 2855.1459219745316, (1, 2099): 2858.0042753742246, (1, 2101): 2854.2960414459453, (1, 2102): 2869.028541708572, (1, 2103): 2864.2751766479537, (1, 2104): 2861.5347043854567, (1, 2106): 2882.568234558045, (1, 2112): 2855.977446851776, (1, 2113): 2870.9425910169543, (1, 2114): 2873.977560575037, (1, 2117): 2884.511632488924, (1, 2123): 2874.2310936458884, (1, 2124): 2877.269770436486, (1, 2134): 2867.932516026688, (1, 2138): 2877.1455605776546, (1, 2141): 2869.1950334332964, (1, 2148): 2870.956398902984, (1, 2150): 2861.67360891384, (1, 2151): 2864.6775876773277, (1, 2152): 2859.813624819368, (1, 2153): 2872.2421388422476, (1, 2154): 2859.825112953168, (1, 2155): 2857.9151458147717, (1, 2156): 2855.903337776585, (1, 2157): 2857.3990554059715, (1, 2160): 2880.1159995674466, (1, 2161): 2859.0265208614537, (1, 2162): 2871.732013970624, (1, 2163): 2867.5571399166497, (1, 2164): 2867.103719145589, (1, 2168): 2861.53625328704, (1, 2172): 2863.131520452793, (1, 2174): 2863.9766788466422, (1, 2178): 2865.256015854671, (1, 2179): 2863.1871788184867, (1, 2183): 2876.633359566501, (1, 2185): 2876.661664175584, (1, 2186): 2874.3228681820437, (1, 2190): 2881.002894100033, (1, 2192): 2876.7358493427096, (1, 2193): 2877.5762099008316, (1, 2194): 2873.215533167206, (1, 2195): 2872.2357596387956, (1, 2197): 2877.4981059950055, (1, 2205): 2870.8989431762643, (1, 2207): 2862.4206894027056, (1, 2208): 2867.092129560132, (1, 2212): 2879.610405268512, (1, 2214): 2785.2359119026473, (1, 2225): 2794.715683482029, (1, 2231): 2781.522837182854, (1, 2278): 2835.904452003742, (1, 2284): 2844.280692844095, (1, 2285): 2842.758141505255, (1, 2291): 2823.0953258078307, (1, 2292): 2827.1677196674796, (1, 2307): 2838.36825557005, (1, 2313): 2820.306696374127, (1, 2317): 2821.35330334016, (1, 2319): 2830.061504373351, (1, 2321): 2833.8501748519284, (1, 2323): 2833.899790726757, (1, 2326): 2850.757149700706, (1, 2327): 2846.8582643955683, (1, 2329): 2844.136317140338, (1, 2330): 2840.8964186838266, (1, 2332): 2847.0416251670777, (1, 2344): 2837.9473090805686, (1, 2346): 2837.354861532475, (1, 2361): 2839.214950254007, (1, 2368): 2882.777252801249, (1, 2374): 2886.7522819872547, (1, 2375): 2888.3920382192505, (1, 2377): 2873.7218472865543, (1, 2378): 2890.9172154745143, (1, 2379): 2890.8799528803866, (1, 2380): 2892.6511898187136, (1, 2383): 2877.9623104236534, (1, 2385): 2880.4148277796617, (1, 2395): 2881.0334767318254, (1, 2397): 2888.9144633129094, (1, 2398): 2869.002537562423, (1, 2399): 2874.5672276640435, (1, 2400): 2873.3703197400705, (1, 2402): 2880.7497789760123, (1, 2403): 2884.0577504634853, (1, 2404): 2885.080628963709, (1, 2405): 2876.9549516397665, (1, 2407): 2883.8213296681693, (1, 2408): 2887.52726246017, (1, 2409): 2879.4847472808174, (1, 2411): 2883.336435965464, (1, 2412): 2882.7305874759227, (1, 2413): 2885.3483902067596, (1, 2414): 2880.841374434731, (1, 2422): 2882.084474422138, (1, 2424): 2883.8175139007653, (1, 2426): 2884.6762111532926, (1, 2433): 2878.2308216228903, (1, 2436): 2876.130083214844, (1, 2437): 2856.917028465712, (1, 2440): 2861.276183477403, (1, 2445): 2942.9062529588646, (1, 2447): 2932.816688232058, (1, 2454): 2942.7301737673574, (1, 2455): 2943.642442484719, (1, 2460): 2912.377117094804, (1, 2461): 2916.1570901219056, (1, 2471): 2975.5697439845994, (1, 2492): 2894.8901482845918, (1, 2511): 2866.762290457556, (1, 2523): 2881.096740104063, (1, 2525): 2875.5506791546436, (1, 2535): 2892.1120114406003, (1, 2537): 2885.024025800394, (1, 2538): 2890.321686698856, (1, 2539): 2886.301549584493, (1, 2540): 2895.2763364495304, (1, 2542): 2899.703531492056, (1, 2559): 3001.7676226245208, (1, 2575): 2990.5119748706247, (1, 2599): 2847.784400140052, (1, 2600): 2879.6852651110453, (1, 2607): 2862.735192484855, (1, 2627): 2878.1986057431977, (1, 2647): 2894.7785869877503, (1, 2674): 2887.8788892423886, (1, 2681): 2884.2072429739733, (1, 2683): 2893.5575645213307, (1, 2686): 2883.981306496051, (1, 2689): 3000.7138798272485, (1, 2690): 3001.0033744247357, (1, 2713): 3015.223723613159, (1, 2714): 3016.0275036728135, (1, 2715): 3018.984334029063, (1, 2739): 3016.708972538335, (1, 2740): 3001.321620853854, (1, 2741): 3003.0210561177696, (1, 2749): 3011.3859009676557, (1, 2750): 3012.7281696342648, (1, 2752): 3015.0254610300003, (1, 2755): 3017.097436457197, (1, 2758): 3016.063483613998, (1, 2759): 3016.2619244497732, (1, 2769): 3013.307752601298, (1, 2771): 3005.245507792669, (1, 2779): 3003.1420918792846, (1, 2784): 2968.6434755569294, (1, 2800): 2971.562678484339, (1, 2802): 2994.008483076344, (1, 2803): 2993.2625795095914, (1, 2804): 2991.4418834657595, (1, 2805): 2995.3548020267785, (1, 2807): 2995.5522283807654, (1, 2809): 2993.6038661388516, (1, 2812): 2975.6649248088424, (1, 2814): 2990.0722198689414, (1, 2817): 2987.263640957613, (1, 2819): 2996.8678182459607, (1, 2823): 2974.1980994720093, (1, 2832): 2998.474622291751, (1, 2836): 2985.26456107913, (1, 2839): 2995.8960274519245, (1, 2841): 2989.6748598765903, (1, 2843): 2989.3105443739146, (1, 2846): 2986.327413514092, (1, 2849): 2999.890652048979, (1, 2852): 2997.1353564787587, (1, 2853): 3001.1351983472714, (1, 2876): 3000.681363869543, (1, 2877): 3011.0136583194985, (1, 2885): 3010.5367462194636, (1, 2918): 3000.778725220058, (1, 2921): 3004.8885281934786, (1, 2925): 2986.776014192007, (1, 2926): 2981.385403022724, (1, 2930): 2991.6005431250355, (1, 2931): 2987.731089901753, (1, 2938): 3000.1861085383393, (1, 2940): 3016.4604009595687, (1, 2947): 3001.711108165275, (1, 2949): 2992.9364600442445, (1, 2950): 2994.3455328967243, (1, 2952): 2992.0804150204985, (1, 2958): 2991.90520680088, (1, 2959): 2994.807597920815, (1, 2960): 2999.564984536282, (1, 2961): 2996.8710048261196, (1, 2963): 2989.6326377373766, (1, 2968): 2990.6823653751285, (1, 2976): 2989.422171908487, (1, 2981): 2942.0060142387724, (1, 2982): 2940.001123429722, (1, 2984): 2937.592074259026, (1, 3003): 2932.818239694382, (1, 3046): 2912.234161520563, (1, 3050): 2931.1434105048265, (1, 3051): 2933.196644123782, (1, 3053): 2927.9530793224726, (1, 3069): 2954.2352105998775, (1, 3071): 2928.4829630635354, (1, 3080): 3009.2755405740036, (1, 3199): 2920.8036652774076, (1, 3200): 2915.0572605124307, (1, 3205): 2947.696039671814, (1, 3209): 2917.6987445864147, (1, 3215): 2915.806446373061, (1, 3217): 2909.2582195300292, (1, 3249): 2916.8492910265263, (1, 3263): 2966.4875097459876, (1, 3289): 2933.6641127858275, (1, 3301): 2934.138979360748, (1, 3302): 2932.1840139669, (1, 3307): 2929.360352456783, (1, 3310): 2936.9567407977524, (1, 3391): 2921.1568480036613, (1, 3509): 1911.485820476725, (1, 3510): 1906.933111354727, (1, 3511): 1910.5373619325464, (1, 3512): 1908.2214019647624, (1, 3514): 1909.6303647576392, (1, 3519): 1919.360438019256, (1, 3536): 1920.5246493207749, (1, 3545): 1928.2468371160164, (1, 3548): 1922.0062270572676, (1, 3572): 1922.4177238305583, (1, 3581): 1914.9913834796691, (1, 3583): 1914.2466717767545, (1, 3601): 1927.0238253388213, (1, 3656): 1917.421130679091, (1, 3669): 1903.7113122218746, (1, 3670): 1907.5905932097128, (1, 3695): 1886.2790802020645, (1, 3696): 1889.58884611621, (1, 3782): 1933.3460294707572, (1, 3792): 1926.8823390863608, (1, 3989): 93.39218229528363, (1, 4008): 102.65867282880642, (1, 4031): 89.58565697015526, (1, 4045): 97.39130892407886, (1, 4144): 111.3177288181251, (1, 4145): 122.96281168743579, (1, 4164): 112.31910063695385, (1, 4168): 118.59008117142709, (1, 4173): 122.3128086776524, (1, 4181): 121.74407473565964, (1, 4228): 104.43955545752009, (1, 4248): 130.80653166715743, (1, 4254): 276.93767703975357, (1, 4260): 269.0635347073173, (1, 4262): 267.86637284846717, (1, 4273): 264.30591583328646, (1, 4319): 365.01176123615267, (1, 4326): 365.5912895495821, (1, 4328): 362.7246806583792, (1, 4334): 364.18287022570377, (1, 4335): 367.13623192464166, (1, 4372): 1142.9430413300859, (1, 4413): 1191.1804206613783, (1, 4434): 1136.2418041785818, (1, 4447): 1122.4589744145612, (1, 4452): 1139.3018235557217, (1, 4463): 1206.9495539050738, (1, 4465): 1201.3782644288049, (1, 4619): 1248.656647205329, (1, 4645): 1242.0586645781254, (1, 4657): 1248.547634338545, (1, 4666): 1253.8944274753608, (1, 4676): 1254.9980850449194, (1, 4678): 1252.054564728758, (1, 4689): 1259.2997824179254, (1, 4704): 1267.2887790912216, (1, 4726): 1438.4887416474237, (1, 4727): 1435.8670593040194, (1, 4730): 1430.3492886060574, (1, 4731): 1434.8378854839486, (1, 4734): 1421.0624149234534, (1, 4735): 1421.0895420339714, (1, 4736): 1424.5180180438324, (1, 4737): 1423.0816359225, (1, 4738): 1425.4264165201164, (1, 4756): 1429.3755816459045, (1, 4760): 1404.0148647867345, (1, 4761): 1400.5505007178995, (1, 4762): 1403.456214984691, (1, 4765): 1406.7713402747331, (1, 4773): 1441.2314359480374, (1, 4774): 1442.8919229302885, (1, 4790): 1438.887304434555, (1, 4795): 1435.5933191845065, (1, 4799): 1446.1427462818901, (1, 4801): 1457.0990757099576, (1, 4804): 1431.4698853422965, (1, 4805): 1428.8211885880505, (1, 4806): 1447.7903759471246, (1, 4815): 1448.7965185970045, (1, 4816): 1453.53835508219, (1, 4817): 1459.4261860625602, (1, 4826): 1454.108264420846, (1, 4830): 1452.3532077412256, (1, 4839): 1411.8292552643873, (1, 4840): 1416.1477908907677, (1, 4841): 1412.2773080620248, (1, 4846): 1409.6898567305816, (1, 4848): 1413.1099416372624, (1, 4850): 1416.1536699579103, (1, 4871): 1367.771869792685, (1, 4883): 1395.2383867344122, (1, 4900): 1375.4140609535928, (1, 4901): 1375.4305672525654, (1, 4917): 1326.9757876490175, (1, 4931): 1315.4985512715125, (1, 4944): 1325.3240166456937, (1, 4956): 1320.5461182695153, (1, 4958): 1326.0748750509965, (1, 4959): 1327.9317217487485, (1, 4961): 1320.4626034153737, (1, 4966): 1321.1688965056785, (1, 5207): 1309.4202473875841, (1, 5272): 966.3487259655419, (1, 5283): 969.6342364918354, (1, 5287): 989.1136051705857, (1, 5289): 991.1665051887342, (1, 5293): 953.1692120853899, (1, 5295): 960.4735049411815, (1, 5296): 969.0375072518351, (1, 5298): 973.7510654556704, (1, 5303): 983.4075935991978, (1, 5305): 981.5097542064467, (1, 5306): 991.6610233390173, (1, 5307): 980.9101306407485, (1, 5308): 985.501015035913, (1, 5313): 974.5656692425018, (1, 5314): 972.9678945954593, (1, 5317): 991.1179821620411, (1, 5319): 982.8167252950755, (1, 5324): 974.6967693249978, (1, 5326): 968.9857679002097, (1, 5348): 998.4390963793757, (1, 5351): 1012.3511278710629, (1, 5399): 1005.3380336591254, (1, 5413): 1034.7268088915077, (1, 5422): 998.3017978531041, (1, 5445): 995.888820359654, (1, 5448): 993.5370816148363, (1, 5456): 1002.084363316319, (1, 5467): 1006.6902936273758, (1, 5624): 955.7474898285342, (1, 5671): 921.3599038422922, (1, 5672): 915.4315252643155, (1, 5797): 993.0192331044217, (1, 5871): 1127.9548251400147, (1, 5976): 1096.2972182107906, (1, 6118): 2424.0204273433887, (1, 6248): 2508.886366794803, (1, 6345): 856.2996144007741, (1, 6352): 876.0955068677781, (1, 6354): 852.0153849277475, (1, 6359): 847.2128544051054, (1, 6376): 870.9418478695973, (1, 6378): 854.2335488212182, (1, 6381): 848.1831924714286, (1, 6383): 860.8387800206494, (1, 6396): 847.0442649092215, (1, 6399): 854.974075384468, (1, 6408): 876.2279695181405, (1, 6409): 869.363622508206, (1, 6419): 904.8847362470899, (1, 6422): 875.4873945832287, (1, 6423): 877.2093009416816, (1, 6424): 856.7883226436654, (1, 6439): 861.3565640471982, (1, 6464): 867.550617701489, (1, 6465): 868.6044069596583, (1, 6469): 864.3443978984517, (1, 6470): 865.1366956513905, (1, 6472): 840.2075597317933, (1, 6480): 848.5324386714742, (1, 6486): 842.2204676457428, (1, 6497): 844.4770143957826, (1, 6503): 871.7789671275984, (1, 6508): 867.375686584731, (1, 6509): 865.0463074918343, (1, 6521): 848.1651921390463, (1, 6544): 852.4384179582657, (1, 6552): 876.6372531409953, (1, 6553): 879.9325704558892, (1, 6554): 883.2497983952106, (1, 6578): 870.7297180447193, (1, 6582): 876.0548462402382, (1, 6601): 869.8396161601441, (1, 6609): 840.9876954328274, (1, 6610): 840.6771003395426, (1, 6611): 838.5018480145377, (1, 6614): 839.2853797836133, (1, 6615): 839.2084596703475, (1, 6616): 837.8621992949443, (1, 6617): 838.6099745793434, (1, 6618): 836.003012732861, (1, 6619): 841.9194209921603, (1, 6620): 838.7875595028219, (1, 6621): 841.7056294538589, (1, 6622): 840.3796663028227, (1, 6623): 840.5881760452197, (1, 6624): 844.0099624348077, (1, 6625): 844.0104353340834, (1, 6626): 841.674853252701, (1, 6627): 839.1712243001233, (1, 6628): 840.3853630270663, (1, 6629): 844.4459111513506, (1, 6630): 844.8870074130444, (1, 6632): 844.1808681607439, (1, 6634): 848.4282184392647, (1, 6635): 842.1429436615261, (1, 6636): 838.0510819246107, (1, 6637): 848.2899644564076, (1, 6638): 845.4199347010135, (1, 6639): 839.4119679237047, (1, 6640): 844.4952306030854, (1, 6641): 842.568644973373, (1, 6642): 845.9760387879959, (1, 6643): 841.3471688761061, (1, 6645): 841.9550615180704, (1, 6646): 836.181601522457, (1, 6647): 844.80650072604, (1, 6653): 839.0478487238512, (1, 6655): 839.0876582838603, (1, 6658): 848.9883246944811, (1, 6662): 846.810201981249, (1, 6819): 1015.5659409761558, (1, 6996): 979.6081685811015, (1, 7059): 943.6060199326128, (1, 7187): 1056.2682754124, (1, 7304): 1099.6795837692832, (1, 7528): 1002.7884142090601, (1, 7720): 778.531007545963, (1, 7793): 792.7983210372903, (1, 7807): 786.692374659403, (1, 7808): 796.2206225673642, (1, 7831): 828.4924086691573, (1, 7850): 788.3211953583047, (1, 7852): 794.7826187681485, (1, 8012): 775.2068945611971, (1, 8125): 826.9412669353088, (1, 8208): 719.5451733530829, (1, 8392): 823.682314756078, (1, 8651): 1196.4103375219645, (1, 9088): 1014.2980923655413, (1, 9443): 1335.1642770503033, (1, 9444): 1331.110274587005, (1, 9828): 1523.1800228843695, (1, 9868): 1500.5461969057942, (1, 10180): 830.6995296045751, (1, 10256): 767.0612067086142, (1, 10276): 782.7028425059226, (1, 10378): 734.7076048709822, (1, 10676): 916.7371432737646, (1, 10714): 978.9227172911061, (1, 10730): 924.926966370657, (1, 10862): 1488.7190247049746, (1, 10881): 1486.52444662538, (1, 10883): 1489.1343282984496, (1, 10885): 1488.6119280192815, (1, 10891): 1493.2508551997428, (1, 10909): 1487.7950373711744, (1, 10911): 1481.6893331986334, (1, 10913): 1484.0681295661689, (1, 10915): 1481.1028248719222, (1, 10919): 1478.2847578319336, (1, 11037): 1565.196195227881, (1, 11039): 1547.609335439936, (1, 11516): 341.3947546756571, (1, 11856): 363.30525083619193, (1, 11857): 375.1991768771642, (1, 11861): 369.4233019718531, (1, 11881): 357.9390810912551, (1, 11902): 365.3242453358998, (1, 11911): 357.1002314735368, (1, 11914): 360.1871850000967, (1, 11922): 357.9349071652595, (1, 11924): 353.67131062449454, (1, 11926): 355.19839467574207, (1, 11950): 340.15559373446115, (1, 11963): 335.13701066202566, (1, 11983): 321.6322284568574, (1, 11985): 333.8243734968069, (1, 12009): 319.40465013643865, (1, 12010): 326.79436028315877, (1, 12018): 324.12923691613196, (1, 12020): 325.28522866381707, (1, 12021): 323.0016665780951, (1, 12024): 319.62518276080056, (1, 12025): 323.8759946668791, (1, 12027): 323.8817127630257, (1, 12031): 327.53803934370933, (1, 12032): 328.6323497315161, (1, 12035): 316.12408322882646, (1, 12041): 342.6437241389148, (1, 12045): 399.1352297316818, (1, 12145): 345.50071889111973, (1, 12275): 71.00133997676488, (1, 12294): 33.977508031636575, (1, 12358): 120.12591925424228, (1, 12463): 154.88212708037634, (1, 12465): 153.92679270337192, (1, 12482): 169.0963023119747, (1, 12503): 166.78160472895047, (1, 12506): 170.95833550727698, (1, 12549): 163.69165629585743, (1, 12559): 159.88922017846454, (1, 12569): 162.62050043340636, (1, 12572): 165.8259923764091, (1, 12574): 159.31484326689673, (1, 12576): 167.78971667820005, (1, 12591): 169.4277472868415, (1, 12608): 197.8229620676769, (1, 12696): 158.44593602710748, (1, 12710): 188.6851367991377, (1, 12728): 170.57812996006453, (1, 12766): 521.5128590611723, (1, 12771): 551.0998292138448, (1, 12790): 555.2545250780041, (1, 12795): 564.8589598814618, (1, 12797): 605.0992169699518, (1, 12798): 599.664634514422, (1, 12811): 567.6827672500006, (1, 12830): 578.2119687000794, (1, 12848): 573.1159455903418, (1, 12850): 570.9086594876632, (1, 12852): 579.8324880557471, (1, 12854): 584.7325820955871, (1, 12859): 568.4300598554765, (1, 12861): 594.3665512967976, (1, 12865): 561.5131654038424, (1, 12866): 564.1281057955874, (1, 12867): 554.2333926655374, (1, 12874): 559.0147470191641, (1, 12875): 555.3506580344057, (1, 12881): 570.4432086319299, (1, 12883): 564.397554667695, (1, 12885): 552.1124710077358, (1, 12888): 567.2596869174038, (1, 12889): 568.6995936540402, (1, 12892): 557.9326568705466, (1, 12893): 566.9788032939166, (1, 12896): 564.1198361947194, (1, 12906): 558.5767988495325, (1, 13018): 607.3490009119176, (1, 13071): 609.3143536870787, (1, 13131): 641.6072569569784, (1, 13146): 609.2205582271531, (1, 13159): 660.4061701136081, (1, 13193): 647.7170393479746, (1, 13198): 704.338061606558, (1, 13292): 639.8345157343819, (1, 13296): 623.6095563973023, (1, 13406): 739.3995842202828, (1, 13407): 741.3684126685556, (1, 13417): 747.2947459714832, (1, 13418): 741.6328431899329, (1, 13438): 715.3838399842084, (1, 13442): 710.0286509056591, (1, 13443): 714.8231915148112, (1, 13764): 1153.8533390088319, (1, 13766): 1147.661200862231, (1, 13771): 1155.8675641168488, (1, 13783): 1155.6256210390266, (1, 13784): 1140.002818564679, (1, 13792): 1171.2252582763952, (1, 13824): 1160.2687591662407, (1, 14017): 1113.9935938344715, (1, 14870): 1368.8374957472715, (1, 14997): 1086.2001624682005, (1, 15000): 1087.4774851867987, (1, 15003): 1085.6615767869628, (1, 15006): 1069.3720025207872, (1, 15007): 1065.826654974353, (1, 15056): 1071.798863668455, (1, 15063): 1076.204100534232, (1, 15069): 1079.5851640395404, (1, 15076): 1066.51714073245, (1, 15086): 1075.9478068394162, (1, 15087): 1082.4539482229975, (1, 15111): 1091.9333045771662, (1, 15116): 1086.6573126394323, (1, 15722): 1185.4361130132409, (1, 15998): 1298.1064726050276, (1, 16073): 2033.2099167515685, (1, 16939): 2629.7541101945803, (1, 16940): 2624.002972695055, (1, 16951): 2629.209915636124, (1, 16963): 2630.094616058703, (1, 16965): 2637.6835287902068, (1, 16969): 2635.140616552414, (1, 16970): 2633.102496058399, (1, 16971): 2626.314012997848, (1, 16973): 2625.375761520174, (1, 16974): 2640.271859018336, (1, 16976): 2633.9333972937025, (1, 16978): 2629.1424821849973, (1, 16980): 2636.850866497533, (1, 16982): 2639.7148012034395, (1, 17045): 2802.898419037372, (1, 17048): 2811.3481601718713, (1, 17304): 163.61065856652388, (1, 17305): 152.8717014314955, (1, 17330): 155.704501924468, (1, 17334): 167.22925413871252, (1, 17343): 152.40480996116526, (1, 17345): 155.30370802872145, (1, 17347): 147.95034788100688, (1, 17351): 169.94766793671056, (1, 17372): 162.8832632220217, (1, 17373): 154.32685242333187, (1, 17377): 152.77403971717308, (1, 17382): 155.6281907067852, (1, 17383): 159.10323561319996, (1, 17389): 159.9801711627398, (1, 17400): 158.88523912549812, (1, 17401): 160.8662727807725, (1, 17402): 157.55291137716114, (1, 17403): 156.29971514781346, (1, 17440): 142.20420784798281, (1, 17455): 144.88394148971813, (1, 17491): 135.70438044717775, (1, 17507): 197.08587505592527, (1, 17509): 198.93431878854707, (1, 17590): 158.06132305942413, (1, 17615): 244.00592746495292, (1, 17642): 236.1733394420727, (1, 17643): 231.78143121631553, (1, 17668): 246.94162139864346, (1, 17721): 277.1730804553642, (1, 17754): 271.43141308598814, (1, 17769): 210.57051108916747, (1, 17776): 194.48728837799374, (1, 17804): 211.10913776628166, (1, 17809): 210.31966610622504, (1, 17824): 218.65489542048084, (1, 17837): 185.52395662304266, (1, 17838): 178.60577901217295, (1, 17862): 176.48073704159557, (1, 17866): 176.7976320349312, (1, 17872): 181.66339734784015, (1, 17873): 180.5831611772076, (1, 17881): 181.44185857863192, (1, 17947): 2165.030682255718, (1, 17951): 2153.216788382676, (1, 17953): 2151.2475210938032, (1, 17954): 2152.2621414432756, (1, 17959): 2162.108963765782, (1, 17963): 2157.441023693958, (1, 18000): 2098.148397561259, (1, 18001): 2100.9068207567734, (1, 18111): 2278.8300314316957, (1, 18148): 1984.4890913182637, (1, 18166): 2100.028236552415, (1, 18189): 2204.4377418974914, (1, 18239): 158.5143530156148, (1, 18240): 157.15343643132812, (1, 18245): 157.73274105120058, (1, 18247): 156.44673501575733, (1, 18251): 156.06765861551034, (1, 18256): 154.06820949161357, (1, 18258): 153.47083492883425, (1, 18259): 152.69789174228094, (1, 18260): 151.59048985128277, (1, 18262): 150.4965712797868, (1, 18263): 153.2387120121749, (1, 18264): 152.22841522673912, (1, 18266): 149.22190079802502, (1, 18267): 148.42705872096658, (1, 18268): 147.52522587516816, (1, 18269): 145.79996009139427, (1, 18275): 146.60712897811223, (1, 18285): 153.11262900567664, (1, 18308): 171.45551133254807, (1, 18313): 173.91924315488228, (1, 18314): 168.53562317522247, (1, 18315): 149.67785876222294, (1, 18316): 147.93860197976124, (1, 18317): 147.017615402684, (1, 18320): 148.81175020355957, (1, 18321): 147.47717288833215, (1, 18322): 146.40468141844917, (1, 18324): 148.1559271011165, (1, 18325): 147.40666588357823, (1, 18326): 147.76652928064493, (1, 18327): 144.6408381148397, (1, 18329): 149.14052720718666, (1, 18330): 143.7740850891157, (1, 18331): 145.18020456551537, (1, 18332): 145.69514885574583, (1, 18333): 145.48704696023557, (1, 18336): 148.65892838663248, (1, 18337): 149.57993736986242, (1, 18403): 139.63823203550535, (1, 18432): 104.03489473221859, (1, 18451): 126.17250057544808, (1, 18466): 159.20305210049222, (1, 18481): 154.34517433749267, (1, 18483): 153.04412572936252, (1, 18484): 154.47828578456355, (1, 18485): 160.16560939600498, (1, 18486): 163.61206800282937, (1, 18487): 166.2368561286203, (1, 18489): 159.30209190996254, (1, 18490): 161.85414091776525, (1, 18491): 161.40543714644414, (1, 18492): 166.2289884742614, (1, 18493): 165.34575390594685, (1, 18494): 158.44239430795957, (1, 18495): 162.39250161579477, (1, 18496): 161.808904747166, (1, 18497): 168.0590435807899, (1, 18498): 162.4875583913446, (1, 18499): 161.22867684347028, (1, 18501): 164.4491487854343, (1, 18502): 165.41163852802387, (1, 18503): 164.5648512172814, (1, 18504): 159.99779192269307, (1, 18506): 168.0980960844136, (1, 18507): 169.7579373045388, (1, 18508): 162.67256612867425, (1, 18509): 163.89964653261217, (1, 18510): 166.3713341156348, (1, 18511): 167.79021398170352, (1, 18512): 166.21931642884377, (1, 18515): 161.7853282130059, (1, 18516): 166.0412284701099, (1, 18517): 169.10633783986293, (1, 18518): 164.26025630545595, (1, 18519): 159.07692515061814, (1, 18520): 161.34090966588806, (1, 18522): 153.46213599827408, (1, 18523): 154.76966253636124, (1, 18532): 155.98642503763924, (1, 18535): 154.9580380941054, (1, 18537): 154.43352339989073, (1, 18539): 155.28660120679305, (1, 18540): 156.13640224640793, (1, 18541): 157.05057550739448, (1, 18542): 157.49950585427985, (1, 18543): 155.8892712463884, (1, 18546): 159.07386110267296, (1, 18555): 160.07395133263833, (1, 18556): 161.24353430127118, (1, 18565): 157.84864187535499, (1, 18567): 160.9869785277817, (1, 18568): 159.1915605669012, (1, 18577): 163.30795966320034, (1, 18583): 158.57101663469658, (1, 18605): 154.7880728754941, (1, 18608): 167.07996934370615, (1, 18616): 160.01220727906846, (1, 18618): 167.70613624087147, (1, 18625): 155.44561920690614, (1, 18645): 146.78699746545743, (1, 18646): 151.3113436239483, (1, 18653): 157.5926624286804, (1, 18654): 161.6033487701583, (1, 18655): 161.0744969552731, (1, 18666): 161.54558736551505, (1, 18837): 11.358565568024492, (1, 18974): 94.40235784222828, (1, 18999): 78.1598811026115, (1, 19000): 78.17516595251502, (1, 19174): 169.49453920709414, (1, 19342): 111.81806784309093, (1, 19455): 146.05857493059182, (1, 19555): 304.57209739313174, (1, 19564): 298.4969638890029, (1, 19573): 304.3731106246684, (1, 19586): 306.7911484794768, (1, 19605): 303.5218644769751, (1, 19611): 299.1395793785509, (1, 19614): 300.254218343158, (1, 19641): 222.75344011913717, (1, 19702): 226.36468126940957, (1, 19713): 231.32223905678762, (1, 19731): 334.2401454194681, (1, 19819): 165.7780366877746, (1, 19893): 668.3793770782108, (1, 19899): 687.4057683544517, (1, 19929): 665.2762069304626, (1, 19951): 678.6624190829751, (1, 19962): 680.7630611067573, (1, 19970): 652.6662599765203, (1, 19971): 659.7279429907027, (1, 19972): 664.0217345577618, (1, 19975): 658.7683051897426, (1, 19978): 649.5954555479212, (1, 19987): 644.9933459132609, (1, 19989): 640.5943928166278, (1, 20039): 643.4979125031331, (1, 20043): 638.7822802736181, (1, 20047): 631.186246430843, (1, 20052): 631.8223723468159, (1, 20054): 635.3431078703529, (1, 20085): 617.965408255645, (1, 20104): 618.7344801859289, (1, 20132): 622.105133277139, (1, 20203): 731.7188821606285, (1, 20280): 751.614650727203, (1, 20285): 760.082490151358, (1, 20290): 747.8582589092906, (1, 20297): 745.834192329025, (1, 20309): 702.5374804534588, (1, 20453): 683.9227241420197, (1, 20485): 737.4238284522253, (1, 20520): 733.4888378670311, (1, 20526): 754.0783376249677, (1, 20698): 1372.2266818532078, (1, 20868): 1592.4713804857556, (1, 21042): 612.177541127122, (1, 21057): 569.3332113723569, (1, 21066): 594.4280141084571, (1, 21075): 596.598374887271, (1, 21093): 614.6203396461991, (1, 21098): 593.5022663785412, (1, 21127): 611.6328884652594, (1, 21130): 606.4264823202943, (1, 21144): 602.2290614729143, (1, 21146): 614.3915271659453, (1, 21147): 601.374134003268, (1, 21148): 595.818438387145, (1, 21153): 594.9778565553806, (1, 21293): 549.6456597712015, (1, 21426): 516.8297819975124, (1, 21442): 465.31081304720806, (1, 21451): 460.49888365178, (1, 21466): 492.5479636048931, (1, 21469): 486.2621688981848, (1, 21471): 495.68392446549075, (1, 21473): 490.8213719138632, (1, 21475): 495.5442737030032, (1, 21482): 481.14308290290387, (1, 21484): 483.05520456367594, (1, 21488): 486.4348542153369, (1, 21494): 497.20893340974453, (1, 21498): 492.12426563601076, (1, 21500): 501.5198692309812, (1, 21514): 495.57802079232766, (1, 21537): 507.0418401741712, (1, 21662): 495.82094951190373, (1, 21691): 520.9935340616189, (1, 21757): 552.7698567569339, (1, 21777): 711.644087692581, (1, 21778): 717.737335252181, (1, 21779): 717.1623706172627, (1, 21790): 701.7519289948183, (1, 21802): 707.6275694269693, (1, 21824): 704.267506977043, (1, 21874): 719.1439473409433, (1, 21879): 728.1322163536519, (1, 21983): 674.187973375138, (1, 22002): 628.6887151616747, (1, 22132): 614.2624495586555, (1, 22261): 1618.264784924583, (1, 22298): 1607.7978313214169, (1, 22339): 1695.4449272459206, (1, 22508): 1485.0322566870943, (1, 22841): 2838.508971395956, (1, 22842): 2839.2274594518726, (1, 22874): 2825.246202214652, (1, 22941): 2824.589943996302, (1, 22956): 2835.152552156836, (1, 22960): 2836.449158863375, (1, 22968): 2855.5450431731097, (1, 22970): 2856.965780633039, (1, 22974): 2867.6005637873222, (1, 22980): 2879.656138885875, (1, 23025): 2886.471668752835, (1, 23028): 2885.4122792421726, (1, 23081): 2915.3283240414376, (1, 23104): 2906.3870780886537, (1, 23147): 2778.2180968051644, (1, 23298): 401.2343879518001, (1, 23376): 419.7059113025262, (1, 23381): 445.48932533794556, (1, 23529): 402.2783523590413, (1, 23556): 410.60586456714026, (1, 23718): 401.4528483963411, (1, 24001): 291.3471031620138, (1, 24094): 295.3516072776536, (1, 24129): 280.629431487958, (1, 24174): 326.7966270028867, (1, 24235): 306.3513106785364, (1, 24259): 282.50043238281813, (1, 24260): 285.1725135344648, (1, 24261): 286.31830316623376, (1, 24305): 263.3030019915257, (1, 24306): 263.40032053384317, (1, 24307): 265.503954385648, (1, 24308): 228.8511222963979, (1, 24498): 197.44999548129587, (1, 24499): 198.09941209522052, (1, 24500): 199.1963835594302, (1, 24668): 173.1572884942056, (1, 24711): 206.668545978677, (1, 24756): 219.93739082910716, (1, 24788): 210.30533849607977, (1, 24809): 236.35835008702975, (1, 24813): 226.58805117400243, (1, 24821): 229.08636308078945, (1, 24825): 230.2867657862708, (1, 24832): 235.73378004386475, (1, 24833): 233.4371258621324, (1, 24835): 232.10488855618513, (1, 24837): 226.3878345830315, (1, 24840): 237.19711093322778, (1, 24841): 231.35882978057097, (1, 24844): 238.59073728799493, (1, 24845): 230.6387109161106, (1, 24846): 239.10021724327717, (1, 24849): 238.59377000212572, (1, 24850): 227.74723954712857, (1, 24863): 251.353325940082, (1, 24866): 246.1265852179327, (1, 24885): 245.39961383934514, (1, 24886): 248.12481900062414, (1, 24889): 227.01191845930296, (1, 24903): 218.27826396488442, (1, 24909): 227.7200353657769, (1, 24999): 155.60897305880158, (1, 25019): 145.24874882345247, (1, 25028): 154.259475000202, (1, 25137): 837.3555508106008, (1, 25145): 834.0576948912644, (1, 25208): 882.0439273803228, (1, 25233): 887.657510247473, (1, 25371): 785.8251004437186, (1, 25377): 779.9487434967515, (1, 25828): 973.0116751464411, (1, 25851): 988.7281425602159, (1, 25874): 957.7116734171374, (1, 25898): 965.998017663767, (1, 25946): 975.4388743248386, (1, 26047): 951.9731870505863, (1, 26066): 742.4315374288287, (1, 26197): 856.4124702428322, (1, 26212): 1182.530702693115, (1, 26253): 1203.6349206426291, (1, 26254): 1193.9376630709542, (1, 26257): 1191.8717143034119, (1, 26258): 1200.9293842093143, (1, 26260): 1195.8717355712074, (1, 26266): 1191.902077984647, (1, 26267): 1187.7357351380379, (1, 26271): 1189.009098601718, (1, 26304): 1109.4739346095205, (1, 26305): 1106.231302614532, (1, 26363): 1015.8145800221862, (1, 26441): 1678.2011983841069, (1, 26442): 1675.8539195600158, (1, 26450): 1665.0926410590046, (1, 26459): 1664.8099161657674, (1, 26462): 1666.5605527225641, (1, 26467): 1698.2361558475704, (1, 26471): 1689.076652325416, (1, 26472): 1688.0538469306887, (1, 26473): 1687.6097069533544, (1, 26476): 1681.7150904261723, (1, 26485): 1669.9081210437384, (1, 26493): 1669.949332737388, (1, 26524): 1671.5580431486749, (1, 26525): 1670.16491824698, (1, 26556): 1684.8198852394726, (1, 26560): 1684.2327310987266, (1, 26561): 1677.4923971757771, (1, 26564): 1681.7709845860738, (1, 26569): 1675.6756478982174, (1, 26570): 1672.7774714494187, (1, 26573): 1674.2852511346812, (1, 26581): 1673.8369640827354, (1, 26583): 1671.5952062037845, (1, 26593): 1673.6612021925905, (1, 26837): 1700.1841233348566, (1, 26844): 1707.5117558145873, (1, 26863): 1691.077506302051, (1, 26893): 1711.9730235227612, (1, 26902): 1721.9083188818897, (1, 26905): 1712.277596333944, (1, 26912): 1719.8974759842408, (1, 26921): 1701.1162802950532, (1, 26922): 1680.515136947439, (1, 27212): 1756.5819397936482, (1, 27218): 1747.8954379482416, (1, 27239): 1770.6311339171357, (1, 27257): 1763.2433294184411, (1, 27274): 1773.4557825422698, (1, 27279): 1771.8144457865085, (1, 27282): 1763.5269654414446, (1, 27283): 1766.9379353236418, (1, 27285): 1777.1654486362415, (1, 27286): 1769.442285149339, (1, 27290): 1756.4306769255495, (1, 27295): 1751.432049958709, (1, 27300): 1774.913253475642, (1, 27344): 1752.3920346627774, (1, 27366): 1761.698270713581, (1, 27383): 1777.7334326942134, (1, 27398): 1788.0233066385883, (1, 27406): 1779.8332578977584, (1, 27407): 1782.3372192008442, (1, 27426): 1771.908399540221, (1, 27432): 1735.9217221128545, (1, 27460): 1758.5193218198413, (1, 27523): 1763.1022474823253, (1, 27545): 1911.5574694169516, (1, 27602): 2099.344734629151, (1, 27606): 2102.861190638252, (1, 27646): 1904.829775765288, (1, 27667): 1942.4061574357454, (1, 27672): 1944.442802200072, (1, 27674): 1937.9968786100715, (1, 27688): 1943.6173684353205, (1, 27692): 1950.8650712524193, (1, 27693): 1945.226906254937, (1, 27705): 1944.8547176621662, (1, 27712): 1947.561341860769, (1, 27786): 2107.8642837240222, (1, 27790): 2086.00859768199, (1, 27791): 2084.113003065016, (1, 27795): 2097.3035181485216, (1, 27801): 2081.1112311911716, (1, 27813): 2113.7356237090275, (1, 27816): 2106.7563761673073, (1, 27823): 2080.4901163817035, (1, 27830): 2098.2931272925457, (1, 27884): 1841.3348267241408, (1, 27885): 1888.9336117346184, (1, 27896): 1860.2139297715316, (1, 27919): 1858.3152350832308, (1, 27922): 1864.1253037993044, (1, 27930): 1848.6789252406656, (1, 27934): 1850.4321632274095, (1, 27935): 1851.6974640235753, (1, 27948): 2076.842992585675, (1, 27951): 2088.6645177013697, (1, 28061): 1875.1240114900136, (1, 28290): 2277.256587104298, (1, 28292): 2283.7974673713697, (1, 28293): 2278.4048947333868, (1, 28295): 2273.957127907704, (1, 28296): 2276.300815979794, (1, 28297): 2273.660707796041, (1, 28302): 2269.8654738051273, (1, 28310): 2302.8052794646637, (1, 28313): 2305.329906128388, (1, 28372): 2313.271237113798, (1, 28398): 2313.395747492033, (1, 28399): 2310.3721372630916, (1, 28400): 2314.386570926421, (1, 28401): 2304.706939866458, (1, 28445): 2299.4006941350704, (1, 28475): 2301.3825758587036, (1, 28885): 377.8248772946725, (1, 28886): 382.8118843022539, (1, 28915): 393.7853967668352, (1, 28916): 391.29563885269636, (1, 28917): 395.0187307115207, (1, 28921): 371.6413117080566, (1, 28931): 375.48094946076566, (1, 28945): 427.1177557508488, (1, 28982): 410.7653375271046, (1, 29219): 472.47160650568674, (1, 29228): 475.15184498732117, (1, 29246): 505.81889117563935, (1, 29248): 520.1375245167825, (1, 29282): 514.4058983621535, (1, 29290): 492.45542645014285, (1, 29291): 495.8123281287287, (1, 29292): 494.7353565713399, (1, 29293): 492.9828727972938, (1, 29294): 500.47442744412, (1, 29298): 496.9061452716019, (1, 29299): 500.61877020159915, (1, 29304): 490.622188319926, (1, 29317): 482.4983055025928, (1, 29323): 481.48379572521304, (1, 29330): 485.8848405048594, (1, 29331): 484.9686651577003, (1, 29344): 499.86826743178574, (1, 29445): 606.7870203909963, (1, 29724): 2778.4892811183922, (1, 29738): 2781.7578968023145, (1, 29745): 2770.960293364817, (1, 29748): 2766.4215362084055, (1, 29750): 2769.047878408107, (1, 29759): 2762.7316906232977, (1, 29772): 2774.7043326373623, (1, 29781): 2771.905418848062, (1, 29784): 2772.612295932603, (1, 29790): 2773.379060149782, (1, 29811): 2763.7043815254174, (1, 29817): 2768.914123856714, (1, 29818): 2766.075390272146, (1, 29929): 2773.8038124727677, (1, 30039): 2833.903350924298, (1, 30066): 2816.3409655331216, (1, 30116): 2691.925958515657, (1, 30238): 2508.7469505532476, (1, 30248): 2616.694192491461, (1, 30260): 2620.2845932641994, (1, 30545): 366.9422980138468, (1, 30733): 473.45787274332133, (1, 30756): 552.7066841255493, (1, 30921): 470.64766401350994, (1, 31079): 834.0293102895956, (1, 31149): 846.4715652456782, (1, 31154): 847.3871032914752, (1, 31160): 847.6175427855688, (1, 31163): 850.0571228651763, (1, 31189): 918.5763787663726, (1, 31215): 915.3916217218601, (1, 31259): 929.8920542582499, (1, 31262): 936.7681129238052, (1, 31430): 834.1510005483399, (1, 31568): 1039.5217724130046, (1, 31751): 875.4537789837281, (3, 109): 156.33938107904038, (3, 872): 1867.8194439121664, (3, 873): 1876.3466797910153, (3, 877): 1874.2593486537232, (3, 879): 1875.6324437991605, (3, 884): 1869.5592768869938, (3, 889): 1874.3718220602868, (3, 891): 1866.4396796138199, (3, 892): 1882.012029469268, (3, 894): 1880.4805934122203, (3, 896): 1870.4198494565862, (3, 903): 1875.8502630596436, (3, 909): 1857.684024956739, (3, 910): 1860.0676483350642, (3, 912): 1854.6710180036578, (3, 913): 1849.1050044946785, (3, 916): 1845.241491255542, (3, 926): 1861.511630123771, (3, 927): 1858.4188843679374, (3, 948): 1863.1703697020191, (3, 961): 1863.6146038019583, (3, 962): 1863.8634921916437, (3, 963): 1864.3754544063627, (3, 967): 1879.0027568657272, (3, 974): 1877.029038821892, (3, 998): 1883.2912089157214, (3, 1014): 2056.5093876522365, (3, 1086): 1817.0115797963572, (3, 1087): 1812.279442703433, (3, 1089): 1806.3512410144335, (3, 1090): 1810.2353817031094, (3, 1092): 1822.498970066537, (3, 1097): 1813.8676867468857, (3, 1107): 1826.2925054709092, (3, 1387): 547.5369792208502, (3, 1554): 454.4126463863044, (3, 1827): 2279.806466146931, (3, 1828): 2280.236663901136, (3, 1829): 2281.868928181904, (3, 1830): 2282.7521456934687, (3, 1831): 2283.119129096305, (3, 1832): 2281.9848326418874, (3, 1833): 2281.704387161978, (3, 1836): 2280.2891607763736, (3, 1841): 2286.3201879265425, (3, 1843): 2284.0294005085793, (3, 1844): 2285.4295129555985, (3, 1845): 2283.0364475464935, (3, 1847): 2273.082709310966, (3, 1848): 2276.2613326148457, (3, 1849): 2291.5360213890817, (3, 1850): 2292.7423564036317, (3, 1851): 2279.713475673829, (3, 1852): 2280.8277551401316, (3, 1854): 2281.6502416567496, (3, 1856): 2273.8028428392167, (3, 1857): 2276.5275818383466, (3, 1858): 2289.475888855995, (3, 1861): 2282.4310735446397, (3, 1866): 2274.366251354712, (3, 1867): 2285.7321101794646, (3, 1868): 2283.1696461404736, (3, 1870): 2286.3166091814546, (3, 1871): 2284.5721094063965, (3, 1875): 2280.8926714900817, (3, 1880): 2274.9868514427994, (3, 1882): 2277.1813735706173, (3, 1883): 2291.858602596156, (3, 1889): 2275.1440805948964, (3, 1893): 2280.591630004188, (3, 1894): 2278.163479441845, (3, 1899): 2272.618769621159, (3, 1900): 2273.919639372734, (3, 1902): 2284.366404627996, (3, 1905): 2287.7512787907704, (3, 1907): 2277.465229631737, (3, 1910): 2277.40592191686, (3, 1917): 2290.7689417575607, (3, 1920): 2276.895146894052, (3, 1935): 2286.433308599119, (3, 1937): 2289.114150065381, (3, 1946): 2265.7821098342165, (3, 1949): 2267.973904930303, (3, 1950): 2260.932628268863, (3, 1951): 2264.81971612286, (3, 1952): 2270.46681584013, (3, 1953): 2269.796702707027, (3, 1954): 2269.245542252377, (3, 1958): 2268.182896429338, (3, 1960): 2273.236549447048, (3, 1968): 2275.225390483586, (3, 1969): 2285.2584813608596, (3, 1974): 2282.7894913094106, (3, 1975): 2283.3339347737747, (3, 1979): 2275.905875420267, (3, 1980): 2277.148791713712, (3, 1981): 2277.892153543827, (3, 1985): 2278.9213978226426, (3, 1994): 2261.3595165997517, (3, 2011): 2277.6622721940157, (3, 2019): 2302.1447397859033, (3, 2020): 2298.921082687461, (3, 2029): 2288.37306741165, (3, 2030): 2296.659307312087, (3, 2032): 2287.524641411126, (3, 2033): 2292.2709657617197, (3, 2034): 2293.027869852006, (3, 2036): 2285.7457321370944, (3, 2037): 2287.4715429440284, (3, 2038): 2284.3879056982523, (3, 2042): 2318.8154240973467, (3, 2050): 2289.4751655727177, (3, 2051): 2289.9019721009327, (3, 2053): 2290.41017298599, (3, 2054): 2293.4876506322375, (3, 2066): 2287.3875104990293, (3, 2067): 2286.9343399874538, (3, 2071): 2255.1667095331927, (3, 2072): 2260.1319861232055, (3, 2073): 2242.25016026891, (3, 2074): 2242.0753930003402, (3, 2080): 2234.0373280606213, (3, 2082): 2263.0176597114114, (3, 2083): 2265.5295768352184, (3, 2089): 2258.716511965272, (3, 2090): 2260.9021381480084, (3, 2092): 2256.6999529376894, (3, 2098): 2236.478301217914, (3, 2099): 2240.2917030971894, (3, 2101): 2236.7053261718747, (3, 2102): 2250.8995349266397, (3, 2103): 2246.768969172867, (3, 2104): 2244.8973862649254, (3, 2106): 2267.8439309631035, (3, 2112): 2239.356376743806, (3, 2113): 2253.4247631883363, (3, 2114): 2258.2660431660847, (3, 2117): 2270.704313062185, (3, 2123): 2217.0128086908403, (3, 2124): 2219.941291302376, (3, 2134): 2213.792927051167, (3, 2138): 2221.5304361223343, (3, 2141): 2214.131923753382, (3, 2148): 2226.9333580241027, (3, 2150): 2207.4130607658376, (3, 2151): 2211.119965713842, (3, 2152): 2206.374724353347, (3, 2153): 2227.1095811615564, (3, 2154): 2214.442457921155, (3, 2155): 2214.487883543202, (3, 2156): 2211.198417427039, (3, 2157): 2219.5401822900635, (3, 2160): 2229.7255852466665, (3, 2161): 2206.7157709448593, (3, 2162): 2230.851939042898, (3, 2163): 2226.4510052828455, (3, 2164): 2226.693914773483, (3, 2168): 2212.971281684428, (3, 2172): 2219.618722122935, (3, 2174): 2211.838303313846, (3, 2178): 2223.1700916636787, (3, 2179): 2221.598983491148, (3, 2183): 2222.3154709320647, (3, 2185): 2223.0264987106793, (3, 2186): 2220.4092056166505, (3, 2190): 2229.368656718997, (3, 2192): 2224.837912669286, (3, 2193): 2222.8422460198035, (3, 2194): 2218.2177976016037, (3, 2195): 2218.678776235649, (3, 2197): 2226.382488724611, (3, 2205): 2221.509568508269, (3, 2207): 2214.8154566415924, (3, 2208): 2218.7846341193936, (3, 2212): 2221.718165186949, (3, 2214): 2148.831389786753, (3, 2225): 2162.813624245304, (3, 2231): 2117.455156630405, (3, 2278): 2214.922119409072, (3, 2284): 2226.04541437786, (3, 2285): 2225.4910178734617, (3, 2291): 2212.005043491984, (3, 2292): 2208.039467829651, (3, 2307): 2220.1517087882935, (3, 2313): 2211.6894359844446, (3, 2317): 2198.755763829276, (3, 2319): 2211.827814382936, (3, 2321): 2217.0859733917246, (3, 2323): 2214.8435352979623, (3, 2326): 2228.010464765915, (3, 2327): 2223.969733712502, (3, 2329): 2221.3847504777555, (3, 2330): 2218.835563150756, (3, 2332): 2226.277953102693, (3, 2344): 2213.5638598521386, (3, 2346): 2214.545809223695, (3, 2361): 2203.2037143056746, (3, 2368): 2255.9797721284785, (3, 2374): 2261.3340172726957, (3, 2375): 2262.243594773309, (3, 2377): 2245.802014539718, (3, 2378): 2265.554441833627, (3, 2379): 2267.118344066021, (3, 2380): 2267.83084159668, (3, 2383): 2249.2542785370665, (3, 2385): 2251.2574104992173, (3, 2395): 2250.487564326721, (3, 2397): 2265.788293640382, (3, 2398): 2240.6934615066307, (3, 2399): 2245.791045384668, (3, 2400): 2244.501959454385, (3, 2402): 2256.727286619396, (3, 2403): 2260.316367629584, (3, 2404): 2260.7625419094898, (3, 2405): 2252.5434276450133, (3, 2407): 2258.545483624206, (3, 2408): 2263.2529944583275, (3, 2409): 2254.85393733953, (3, 2411): 2262.230945749586, (3, 2412): 2260.561645237524, (3, 2413): 2263.7717851289653, (3, 2414): 2259.250046694716, (3, 2422): 2261.815558084934, (3, 2424): 2261.148729314437, (3, 2426): 2261.5311351554606, (3, 2433): 2255.6189760375996, (3, 2436): 2255.116585529643, (3, 2437): 2233.887947013748, (3, 2440): 2238.219539835233, (3, 2445): 2340.8288563063516, (3, 2447): 2328.41683438203, (3, 2454): 2339.0405038085833, (3, 2455): 2338.7145096355894, (3, 2460): 2306.949592963217, (3, 2461): 2311.0707051495865, (3, 2471): 2381.8468092113208, (3, 2492): 2347.850174222978, (3, 2511): 2309.317780793296, (3, 2523): 2329.15698450332, (3, 2525): 2326.161530355092, (3, 2535): 2315.9283175384635, (3, 2537): 2309.3101109518293, (3, 2538): 2312.9785730326766, (3, 2539): 2315.3152465438625, (3, 2540): 2319.044017692933, (3, 2542): 2325.3847281028443, (3, 2559): 2416.9741715772534, (3, 2575): 2413.105484938788, (3, 2599): 2248.239245217826, (3, 2600): 2285.338602895267, (3, 2607): 2260.487079869265, (3, 2627): 2344.9459019273963, (3, 2647): 2366.866456417502, (3, 2674): 2352.383562122279, (3, 2681): 2352.0586160137445, (3, 2683): 2360.259153552912, (3, 2686): 2348.529865070907, (3, 2689): 2473.9551432417156, (3, 2690): 2475.1078612751608, (3, 2713): 2515.4972759904977, (3, 2714): 2519.822196823462, (3, 2715): 2522.741885014331, (3, 2739): 2519.488559909306, (3, 2740): 2494.779083309223, (3, 2741): 2495.788004425547, (3, 2749): 2517.8235600768808, (3, 2750): 2517.9394308182814, (3, 2752): 2519.6611874321206, (3, 2755): 2522.4792110619032, (3, 2758): 2522.4757345653734, (3, 2759): 2522.126685333985, (3, 2769): 2517.815486388296, (3, 2771): 2501.142134293594, (3, 2779): 2507.8870444351714, (3, 2784): 2477.3125664022864, (3, 2800): 2488.9874607582547, (3, 2802): 2492.2069994954495, (3, 2803): 2490.356436624346, (3, 2804): 2488.099505396866, (3, 2805): 2496.894074214318, (3, 2807): 2495.9699983871615, (3, 2809): 2496.5256156840655, (3, 2812): 2475.740330762317, (3, 2814): 2500.424184102044, (3, 2817): 2507.675972661013, (3, 2819): 2494.542230170025, (3, 2823): 2483.9740318869076, (3, 2832): 2501.6035109082795, (3, 2836): 2488.219328299464, (3, 2839): 2495.17669162717, (3, 2841): 2504.9881645070827, (3, 2843): 2502.8153007166648, (3, 2846): 2493.8434535716087, (3, 2849): 2504.9381864919173, (3, 2852): 2501.426351921806, (3, 2853): 2506.600079848956, (3, 2876): 2511.39136923674, (3, 2877): 2522.631882640977, (3, 2885): 2532.8601525085937, (3, 2918): 2491.319321433412, (3, 2921): 2496.834798464414, (3, 2925): 2468.5378410342896, (3, 2926): 2457.700821818184, (3, 2930): 2485.9687774769823, (3, 2931): 2472.5935364400952, (3, 2938): 2492.668994291486, (3, 2940): 2500.057838872129, (3, 2947): 2482.577682382127, (3, 2949): 2482.908329142641, (3, 2950): 2486.2657150751315, (3, 2952): 2484.010672334496, (3, 2958): 2483.04013766023, (3, 2959): 2483.7777018608563, (3, 2960): 2489.3780782532626, (3, 2961): 2487.508198176948, (3, 2963): 2481.8349380058207, (3, 2968): 2484.049910568829, (3, 2976): 2480.4527539799446, (3, 2981): 2446.202138972032, (3, 2982): 2446.479309036002, (3, 2984): 2444.58599481946, (3, 3003): 2442.3302200796784, (3, 3046): 2395.5284341054785, (3, 3050): 2426.8917596456813, (3, 3051): 2428.085920820796, (3, 3053): 2423.77534224131, (3, 3069): 2453.971813956429, (3, 3071): 2419.0922574298093, (3, 3080): 2535.44340517946, (3, 3199): 2444.3243817010043, (3, 3200): 2440.1802320434563, (3, 3205): 2471.1969124693087, (3, 3209): 2443.0550874179526, (3, 3215): 2439.6563292756096, (3, 3217): 2433.5228486732312, (3, 3249): 2439.3267540047855, (3, 3263): 2485.2919032562613, (3, 3289): 2451.573056402448, (3, 3301): 2455.241935641131, (3, 3302): 2452.2223038533443, (3, 3307): 2449.2342598585315, (3, 3310): 2457.88594645557, (3, 3391): 2505.398230045205, (3, 3509): 1418.8979909519724, (3, 3510): 1414.520157594234, (3, 3511): 1416.1150894408981, (3, 3512): 1412.2495453961203, (3, 3514): 1412.1231692778074, (3, 3519): 1435.614462638051, (3, 3536): 1424.3048333933925, (3, 3545): 1429.8544091476404, (3, 3548): 1421.4094670450563, (3, 3572): 1428.392670905338, (3, 3581): 1427.4804083226782, (3, 3583): 1419.0722457207944, (3, 3601): 1445.8745512761614, (3, 3656): 1443.8162076128672, (3, 3669): 1446.2048209628495, (3, 3670): 1450.5825257370739, (3, 3695): 1423.6472038391398, (3, 3696): 1426.5438194134383, (3, 3782): 1400.2164214825605, (3, 3792): 1398.852602637305, (3, 3989): 979.4002359305806, (3, 4008): 1003.9045998542033, (3, 4031): 1012.2802122030213, (3, 4045): 994.0783290257656, (3, 4144): 986.0476476192046, (3, 4145): 951.1717267080211, (3, 4164): 974.1550772821533, (3, 4168): 961.7189910476678, (3, 4173): 957.7700599148048, (3, 4181): 942.8450980073449, (3, 4228): 939.6863581573286, (3, 4248): 918.8126595928003, (3, 4254): 738.4014672565063, (3, 4260): 744.1115047376952, (3, 4262): 749.316998755782, (3, 4273): 750.7801789833492, (3, 4319): 641.3583737251132, (3, 4326): 639.8942141611292, (3, 4328): 642.5018025788869, (3, 4334): 643.3359847703748, (3, 4335): 640.3221696324842, (3, 4372): 343.62587125765856, (3, 4413): 428.53604770862097, (3, 4434): 338.0872508692838, (3, 4447): 341.6260689679675, (3, 4452): 340.2701301622859, (3, 4463): 266.50711319667727, (3, 4465): 265.06537027507756, (3, 4619): 460.99233086559616, (3, 4645): 471.2257758662108, (3, 4657): 472.0321015038964, (3, 4666): 469.383244400961, (3, 4676): 479.0767412716523, (3, 4678): 479.80625581617164, (3, 4689): 476.8651129462981, (3, 4704): 526.4615539820642, (3, 4726): 707.6660328099939, (3, 4727): 704.589636804945, (3, 4730): 698.4293283660995, (3, 4731): 701.4756253298904, (3, 4734): 697.6374375788707, (3, 4735): 695.7927592242123, (3, 4736): 698.1925551980083, (3, 4737): 694.2979567470854, (3, 4738): 695.7484351388811, (3, 4756): 699.4030270433036, (3, 4760): 678.7397535787316, (3, 4761): 678.4215909935639, (3, 4762): 675.7987619850632, (3, 4765): 680.871806737931, (3, 4773): 712.6593613819174, (3, 4774): 711.6246886272709, (3, 4790): 710.3621086162361, (3, 4795): 707.2526103936954, (3, 4799): 713.864810477911, (3, 4801): 722.6782288351102, (3, 4804): 706.1912320489902, (3, 4805): 703.666922527821, (3, 4806): 713.0033442402923, (3, 4815): 711.5909093720268, (3, 4816): 718.5001147661501, (3, 4817): 722.0422180421982, (3, 4826): 716.8313141520895, (3, 4830): 713.3265753176624, (3, 4839): 687.7766704404318, (3, 4840): 691.33469007216, (3, 4841): 685.5348623891863, (3, 4846): 683.0828222911223, (3, 4848): 684.048624688901, (3, 4850): 687.1237646341365, (3, 4871): 644.0717901688821, (3, 4883): 672.9130552051658, (3, 4900): 655.8421262743868, (3, 4901): 653.2942594483482, (3, 4917): 497.9006670875877, (3, 4931): 478.286988412662, (3, 4944): 498.5577924937444, (3, 4956): 483.48399026923795, (3, 4958): 486.1314739448718, (3, 4959): 484.6686104363338, (3, 4961): 486.1503228234019, (3, 4966): 480.57429599724134, (3, 5207): 459.39537437619333, (3, 5272): 30.71497084310535, (3, 5283): 24.62841049044814, (3, 5287): 8.434909431055447, (3, 5289): 10.979411925550595, (3, 5293): 42.92553570733128, (3, 5295): 33.50674501408944, (3, 5296): 25.44098433528568, (3, 5298): 21.11615771484796, (3, 5303): 18.142424642764833, (3, 5305): 20.679614000128986, (3, 5306): 21.469967129425005, (3, 5307): 24.30489789985767, (3, 5308): 15.226251098458514, (3, 5313): 23.8847457815271, (3, 5314): 22.810085005648215, (3, 5317): 12.522117887521501, (3, 5319): 13.211703635856486, (3, 5324): 18.823456264392682, (3, 5326): 24.312931443755726, (3, 5348): 22.836554325107603, (3, 5351): 24.371772075690377, (3, 5399): 20.314357773856724, (3, 5413): 41.596320394160706, (3, 5422): 20.22789888786342, (3, 5445): 3.71325206563586, (3, 5448): 4.590916492146804, (3, 5456): 10.233797040586385, (3, 5467): 13.505070995851222, (3, 5624): 91.61380225799662, (3, 5671): 162.63264594439906, (3, 5672): 156.31430631772253, (3, 5797): 262.8512038536993, (3, 5871): 177.39734900952382, (3, 5976): 109.74850502781904, (3, 6118): 2045.543164800968, (3, 6248): 2171.729298478114, (3, 6345): 718.4407814205266, (3, 6352): 735.2491836721377, (3, 6354): 712.0401485595818, (3, 6359): 712.9384147005936, (3, 6376): 742.6560606121292, (3, 6378): 714.486823067691, (3, 6381): 717.1926150855296, (3, 6383): 720.3210355983817, (3, 6396): 735.6134909770242, (3, 6399): 723.2495999570439, (3, 6408): 730.5139448164667, (3, 6409): 711.6393912943203, (3, 6419): 722.5178302605796, (3, 6422): 719.7176746172476, (3, 6423): 720.4845441500047, (3, 6424): 701.3000301566427, (3, 6439): 700.9655682241286, (3, 6464): 702.2000812549359, (3, 6465): 707.6402151861342, (3, 6469): 713.4898062551965, (3, 6470): 716.3530981261779, (3, 6472): 709.0084869041497, (3, 6480): 694.0047843397466, (3, 6486): 664.6210746417728, (3, 6497): 673.5414541719197, (3, 6503): 679.019294083026, (3, 6508): 689.7688616530417, (3, 6509): 681.0606098131042, (3, 6521): 683.6682142303449, (3, 6544): 673.2273082113136, (3, 6552): 697.3765053921196, (3, 6553): 698.8275558476284, (3, 6554): 700.4682808892728, (3, 6578): 696.6450681944741, (3, 6582): 686.036967193334, (3, 6601): 693.4364061715864, (3, 6609): 692.3380595109106, (3, 6610): 689.284749248824, (3, 6611): 695.5912498573597, (3, 6614): 700.4515186799158, (3, 6615): 697.8196005997888, (3, 6616): 687.3779855874736, (3, 6617): 691.2152226638872, (3, 6618): 679.8865620565858, (3, 6619): 700.3775835668246, (3, 6620): 683.2007421680863, (3, 6621): 683.8526650805952, (3, 6622): 686.3654983201134, (3, 6623): 696.1114588272205, (3, 6624): 693.1291455830963, (3, 6625): 695.6328167383822, (3, 6626): 702.259471374494, (3, 6627): 704.4187557563923, (3, 6628): 679.2926623720563, (3, 6629): 687.6474729654427, (3, 6630): 703.5204783024396, (3, 6632): 690.0923806313347, (3, 6634): 702.5214748033685, (3, 6635): 686.6266588059378, (3, 6636): 685.8604310965044, (3, 6637): 689.2752806995936, (3, 6638): 699.4237609417331, (3, 6639): 701.8603733060773, (3, 6640): 701.2499612065864, (3, 6641): 680.6532851731707, (3, 6642): 696.6499578063135, (3, 6643): 705.360241259947, (3, 6645): 698.2956988098065, (3, 6646): 683.6878727542168, (3, 6647): 697.7162584308065, (3, 6653): 699.1576717203019, (3, 6655): 703.1823138805908, (3, 6658): 701.0305719554872, (3, 6662): 693.7953921375379, (3, 6819): 742.9675287288957, (3, 6996): 649.6265125571318, (3, 7059): 626.09805958442, (3, 7187): 553.8485745921196, (3, 7304): 678.5388276883268, (3, 7528): 599.619334381289, (3, 7720): 522.8639683241098, (3, 7793): 500.6459352098984, (3, 7807): 507.2531148577797, (3, 7808): 495.5611806104928, (3, 7831): 653.12919924869, (3, 7850): 657.9989478461539, (3, 7852): 667.4295066118739, (3, 8012): 560.5843799430186, (3, 8125): 382.92111662510257, (3, 8208): 496.4547512870511, (3, 8392): 574.1827635989458, (3, 8651): 869.2352268143849, (3, 9088): 822.4810758805105, (3, 9443): 804.2451125313444, (3, 9444): 797.6107759083654, (3, 9828): 919.8091375875695, (3, 9868): 960.7266585425439, (3, 10180): 370.4997855501658, (3, 10256): 326.73865228150976, (3, 10276): 364.1002118490576, (3, 10378): 426.6410141360572, (3, 10676): 299.3586530096989, (3, 10714): 326.43658859408697, (3, 10730): 373.9935466311637, (3, 10862): 505.957928429735, (3, 10881): 501.37196209159157, (3, 10883): 504.1631041499518, (3, 10885): 506.42424088418846, (3, 10891): 508.55773473715, (3, 10909): 503.4775411097272, (3, 10911): 497.22431646229705, (3, 10913): 500.09170446669555, (3, 10915): 497.25055587439317, (3, 10919): 494.17955641052305, (3, 11037): 597.7245154976433, (3, 11039): 591.9368776015608, (3, 11516): 1330.3033199450188, (3, 11856): 644.9293277759431, (3, 11857): 634.2571657376295, (3, 11861): 639.5094169948994, (3, 11881): 647.0403739845997, (3, 11902): 635.6171119188414, (3, 11911): 641.7233687232757, (3, 11914): 639.7205336218173, (3, 11922): 645.3391915433127, (3, 11924): 650.1094646768614, (3, 11926): 647.2882067771585, (3, 11950): 662.6288245299762, (3, 11963): 672.2479240203767, (3, 11983): 679.3701758977604, (3, 11985): 676.446420252014, (3, 12009): 686.4010856082407, (3, 12010): 676.5502234487133, (3, 12018): 679.3180625126004, (3, 12020): 679.4520861462174, (3, 12021): 681.9293969349208, (3, 12024): 688.6441405148017, (3, 12025): 683.9169742406593, (3, 12027): 682.9273981911967, (3, 12031): 675.3253499734254, (3, 12032): 675.7135871906721, (3, 12035): 688.7292540826354, (3, 12041): 670.3430705799262, (3, 12045): 598.3841220869787, (3, 12145): 647.813272739033, (3, 12275): 1010.6832919235021, (3, 12294): 1004.6110413344924, (3, 12358): 1077.8179017855252, (3, 12463): 1115.204530530304, (3, 12465): 1115.2392556871605, (3, 12482): 1114.608321135831, (3, 12503): 1115.9396811990841, (3, 12506): 1118.5664510654249, (3, 12549): 1099.5353530550888, (3, 12559): 1100.196873166743, (3, 12569): 1107.0827893506068, (3, 12572): 1108.7827604089644, (3, 12574): 1103.7597629330266, (3, 12576): 1100.2138385864832, (3, 12591): 1092.0934923108828, (3, 12608): 1102.5097403944878, (3, 12696): 1071.9490730578575, (3, 12710): 1076.7605530187125, (3, 12728): 1080.2638544623612, (3, 12766): 762.0871491844687, (3, 12771): 718.9000712822209, (3, 12790): 719.3876862518648, (3, 12795): 725.1796149310952, (3, 12797): 694.9116204516923, (3, 12798): 694.477024620251, (3, 12811): 703.3409469822575, (3, 12830): 707.1799099795643, (3, 12848): 694.6599167412977, (3, 12850): 686.9341067868274, (3, 12852): 702.5526689205267, (3, 12854): 701.3228137943104, (3, 12859): 692.2546225320102, (3, 12861): 692.5868946364603, (3, 12865): 711.1820554847073, (3, 12866): 706.3462955429525, (3, 12867): 712.8253605942689, (3, 12874): 710.2457789162237, (3, 12875): 709.5228361833344, (3, 12881): 710.0875082190597, (3, 12883): 711.2345376341975, (3, 12885): 711.3889526024632, (3, 12888): 707.7474650285682, (3, 12889): 704.6781905887927, (3, 12892): 712.1308748885527, (3, 12893): 710.6496977721644, (3, 12896): 708.5481556472686, (3, 12906): 722.947339708826, (3, 13018): 786.9702048890164, (3, 13071): 803.4196216910902, (3, 13131): 732.5993811019302, (3, 13146): 723.0629435325973, (3, 13159): 802.7215041618887, (3, 13193): 727.1238872796574, (3, 13198): 696.7580040855431, (3, 13292): 692.107015648048, (3, 13296): 664.4087607879595, (3, 13406): 743.5067894520374, (3, 13407): 747.2493941070687, (3, 13417): 776.2912885091027, (3, 13418): 780.6307917617333, (3, 13438): 756.988071247568, (3, 13442): 747.1926744378005, (3, 13443): 748.5823386897397, (3, 13764): 1065.3928961409517, (3, 13766): 1062.0486817786987, (3, 13771): 1074.6222889370697, (3, 13783): 1052.7004975326977, (3, 13784): 1054.3904621517704, (3, 13792): 1095.045609466576, (3, 13824): 1056.897012083689, (3, 14017): 982.7574011213337, (3, 14870): 392.79066032589463, (3, 14997): 567.8888960429797, (3, 15000): 563.1684514552234, (3, 15003): 555.6693972494865, (3, 15006): 567.4956613271486, (3, 15007): 563.8480317823321, (3, 15056): 551.152709132924, (3, 15063): 551.5219966822154, (3, 15069): 547.7449842122646, (3, 15076): 560.2198890459808, (3, 15086): 575.9054094353277, (3, 15087): 573.3177476872377, (3, 15111): 587.4157865637424, (3, 15116): 578.8793997417812, (3, 15722): 672.0871181545267, (3, 15998): 653.8086646630752, (3, 16073): 1793.0350844650868, (3, 16939): 2049.006557757238, (3, 16940): 2042.5931145515412, (3, 16951): 2053.114481272608, (3, 16963): 2052.9350300488845, (3, 16965): 2059.3225273541416, (3, 16969): 2059.4517121385093, (3, 16970): 2054.621332025066, (3, 16971): 2048.7489548493118, (3, 16973): 2049.5164607193947, (3, 16974): 2063.0020802191884, (3, 16976): 2054.3421920225214, (3, 16978): 2049.644507646707, (3, 16980): 2055.52613780714, (3, 16982): 2064.166381283036, (3, 17045): 2344.2908793630263, (3, 17048): 2352.6116851315287, (3, 17304): 871.1748328016137, (3, 17305): 874.9607959834622, (3, 17330): 875.9614140593005, (3, 17334): 863.1714825277143, (3, 17343): 882.4390610737199, (3, 17345): 870.5202951891126, (3, 17347): 880.4311339745617, (3, 17351): 854.0941022770071, (3, 17372): 865.2967428042366, (3, 17373): 880.8936394213421, (3, 17377): 882.607002847334, (3, 17382): 874.0489618832237, (3, 17383): 873.1029463515259, (3, 17389): 868.6696632664909, (3, 17400): 876.1403946272551, (3, 17401): 874.773069868715, (3, 17402): 877.3748224630878, (3, 17403): 878.8406630466984, (3, 17440): 879.2781603112245, (3, 17455): 885.921247335612, (3, 17491): 892.3190519695371, (3, 17507): 840.5384414146208, (3, 17509): 843.1240280467749, (3, 17590): 859.6511039604713, (3, 17615): 785.8337254322905, (3, 17642): 794.1514390420297, (3, 17643): 796.6982419902304, (3, 17668): 783.8104404839246, (3, 17721): 756.7042595991356, (3, 17754): 794.7809027171689, (3, 17769): 833.4393610998848, (3, 17776): 829.5592186518509, (3, 17804): 839.3957638892247, (3, 17809): 843.8834470056922, (3, 17824): 836.2361195727567, (3, 17837): 845.5917638880445, (3, 17838): 850.3531515219836, (3, 17862): 849.1392702692599, (3, 17866): 856.4593632429875, (3, 17872): 843.3876866569495, (3, 17873): 838.8267176421543, (3, 17881): 846.4859899063076, (3, 17947): 1500.0055887825802, (3, 17951): 1491.0620799109338, (3, 17953): 1488.0464264816417, (3, 17954): 1487.8156877191682, (3, 17959): 1500.409688448087, (3, 17963): 1499.535672825314, (3, 18000): 1450.5906851205625, (3, 18001): 1450.5988280062938, (3, 18111): 1532.3885857587911, (3, 18148): 1271.894958619444, (3, 18166): 1364.833217074015, (3, 18189): 1466.7889334607216, (3, 18239): 880.3000309509923, (3, 18240): 881.068845959743, (3, 18245): 881.1413373837768, (3, 18247): 881.0431519066823, (3, 18251): 882.1247311926643, (3, 18256): 884.2546994287991, (3, 18258): 883.6130442258966, (3, 18259): 884.2570044912111, (3, 18260): 885.3097087302388, (3, 18262): 886.7053029459449, (3, 18263): 885.0156411363577, (3, 18264): 886.0099416566798, (3, 18266): 887.7680739479846, (3, 18267): 888.6250288534377, (3, 18268): 889.3534163763003, (3, 18269): 891.1486365557396, (3, 18275): 890.3054063222827, (3, 18285): 885.3477313556489, (3, 18308): 866.4994211491176, (3, 18313): 862.4275291908029, (3, 18314): 866.8564040973421, (3, 18315): 888.7849606297411, (3, 18316): 889.7636258985959, (3, 18317): 890.6726209648566, (3, 18320): 889.9354874480167, (3, 18321): 890.9314796927839, (3, 18322): 892.1399558819969, (3, 18324): 891.5568992579637, (3, 18325): 893.7901567102953, (3, 18326): 892.907460442478, (3, 18327): 892.4248489460713, (3, 18329): 893.5688230905594, (3, 18330): 895.8655157593395, (3, 18331): 893.83191564448, (3, 18332): 892.304763340162, (3, 18333): 894.6564135799551, (3, 18336): 891.7612923707167, (3, 18337): 891.8195215529694, (3, 18403): 896.8625611605942, (3, 18432): 899.0429953051587, (3, 18451): 897.6322286159543, (3, 18466): 893.6723301325201, (3, 18481): 886.4509980937227, (3, 18483): 887.2285778679783, (3, 18484): 885.4020327963927, (3, 18485): 879.1073192243147, (3, 18486): 879.618271175823, (3, 18487): 875.8021314657391, (3, 18489): 881.9271430941095, (3, 18490): 882.6641840224103, (3, 18491): 884.0123152475459, (3, 18492): 873.582023333683, (3, 18493): 878.203690507979, (3, 18494): 882.0139605503985, (3, 18495): 881.5424605994833, (3, 18496): 880.7729703381294, (3, 18497): 874.1963501363032, (3, 18498): 878.0515996347111, (3, 18499): 880.4439447213418, (3, 18501): 877.3247431159583, (3, 18502): 875.7030070414825, (3, 18503): 875.4167604492394, (3, 18504): 882.297059172485, (3, 18506): 875.294438756126, (3, 18507): 873.2990131372601, (3, 18508): 879.3491165390661, (3, 18509): 878.6347511709068, (3, 18510): 874.3559430557934, (3, 18511): 877.0624770406092, (3, 18512): 876.7524940016044, (3, 18515): 881.3276464667402, (3, 18516): 878.867499711069, (3, 18517): 875.6924721803042, (3, 18518): 880.8137356820739, (3, 18519): 883.077772910632, (3, 18520): 879.8375435491614, (3, 18522): 891.0000333696261, (3, 18523): 890.456648568044, (3, 18532): 891.2567909668935, (3, 18535): 888.7189889424864, (3, 18537): 887.3094048423592, (3, 18539): 887.1564911294439, (3, 18540): 886.8474743473621, (3, 18541): 887.1510744663989, (3, 18542): 887.4258993300784, (3, 18543): 885.7136756766721, (3, 18546): 885.0705340788496, (3, 18555): 887.2074596096309, (3, 18556): 887.0140341279517, (3, 18565): 889.9407573024778, (3, 18567): 888.8886390549136, (3, 18568): 888.4374358514283, (3, 18577): 897.2362082582605, (3, 18583): 898.0958287479277, (3, 18605): 902.7636152266471, (3, 18608): 886.2187485282994, (3, 18616): 910.8689946794459, (3, 18618): 916.3577881558467, (3, 18625): 920.1322542755837, (3, 18645): 916.5010954696872, (3, 18646): 916.0651237327802, (3, 18653): 904.3142413157885, (3, 18654): 909.6790410942469, (3, 18655): 904.8730742352043, (3, 18666): 938.1235778892473, (3, 18837): 1004.6414370968618, (3, 18974): 917.5583334030824, (3, 18999): 933.9339846809346, (3, 19000): 936.2110109758763, (3, 19174): 898.0361897474601, (3, 19342): 957.0891356399793, (3, 19455): 866.4118756042174, (3, 19555): 812.8976430557107, (3, 19564): 847.7413022775538, (3, 19573): 837.9265602361875, (3, 19586): 831.5823480379363, (3, 19605): 827.9936177393286, (3, 19611): 833.4836607718323, (3, 19614): 822.7421296466821, (3, 19641): 879.8703129636682, (3, 19702): 888.0296124454309, (3, 19713): 881.8348377493503, (3, 19731): 755.1453073265484, (3, 19819): 869.5015762245441, (3, 19893): 339.2623864380083, (3, 19899): 342.14569850504444, (3, 19929): 345.5400159294073, (3, 19951): 376.61098301428984, (3, 19962): 336.114489271568, (3, 19970): 365.03001406825655, (3, 19971): 359.8410872020377, (3, 19972): 353.6527036444185, (3, 19975): 356.3510578477844, (3, 19978): 405.5400282857092, (3, 19987): 409.35238091096414, (3, 19989): 399.48121441683116, (3, 20039): 412.80138709276673, (3, 20043): 421.55053327458995, (3, 20047): 422.12014685806577, (3, 20052): 407.66175061372394, (3, 20054): 406.29755155411704, (3, 20085): 489.87426459709513, (3, 20104): 494.6143518757026, (3, 20132): 462.02463301898337, (3, 20203): 288.39105109074563, (3, 20280): 269.6063229622368, (3, 20285): 262.4266507496246, (3, 20290): 274.20179977961726, (3, 20297): 272.09070470456106, (3, 20309): 377.259203685153, (3, 20453): 475.4241202254207, (3, 20485): 261.9533770394054, (3, 20520): 261.7930343570603, (3, 20526): 241.63314463771843, (3, 20698): 1313.6494591176574, (3, 20868): 1467.548990548921, (3, 21042): 518.0185025000055, (3, 21057): 533.7936595833924, (3, 21066): 516.5461103447923, (3, 21075): 526.7715401383999, (3, 21093): 506.39275054630014, (3, 21098): 498.78215107558464, (3, 21127): 512.4287923583811, (3, 21130): 508.9286085952527, (3, 21144): 520.4798838868875, (3, 21146): 511.58457712875304, (3, 21147): 523.8200982385067, (3, 21148): 522.159309855342, (3, 21153): 562.8795517866992, (3, 21293): 528.8802390733672, (3, 21426): 637.6845197895369, (3, 21442): 677.8977395343784, (3, 21451): 681.3863219106063, (3, 21466): 651.4814118239112, (3, 21469): 652.0208963965541, (3, 21471): 651.4758029318288, (3, 21473): 650.534964125025, (3, 21475): 649.8767282887833, (3, 21482): 656.8885915968823, (3, 21484): 654.3949209654878, (3, 21488): 655.2789129556824, (3, 21494): 643.6088751093057, (3, 21498): 645.5866144193047, (3, 21500): 637.5212230938713, (3, 21514): 618.1575742432374, (3, 21537): 623.1385730724733, (3, 21662): 603.5750352815545, (3, 21691): 595.8287848919323, (3, 21757): 632.4654094981349, (3, 21777): 460.65978576998333, (3, 21778): 460.9340458881407, (3, 21779): 454.82247229288663, (3, 21790): 466.9276949552768, (3, 21802): 455.25457587750134, (3, 21824): 449.23630765102166, (3, 21874): 447.4445853886892, (3, 21879): 436.7177640138567, (3, 21983): 496.6614182789296, (3, 22002): 463.38965371135015, (3, 22132): 595.844583982619, (3, 22261): 905.0172586498381, (3, 22298): 887.2379576944318, (3, 22339): 949.9566505194629, (3, 22508): 784.9909324512711, (3, 22841): 2567.2713070826826, (3, 22842): 2566.6526898800826, (3, 22874): 2548.3515412486613, (3, 22941): 2552.2198911873434, (3, 22956): 2561.468573891337, (3, 22960): 2565.9252995130314, (3, 22968): 2566.608750338024, (3, 22970): 2570.6079211968345, (3, 22974): 2569.6972277931486, (3, 22980): 2581.4135000560686, (3, 23025): 2571.819410086858, (3, 23028): 2567.445309972528, (3, 23081): 2576.4899702680527, (3, 23104): 2540.3566365647584, (3, 23147): 2461.710522250492, (3, 23298): 632.8025323560286, (3, 23376): 621.360889084345, (3, 23381): 588.2791207138243, (3, 23529): 619.0878436279031, (3, 23556): 615.5109495386655, (3, 23718): 647.544327819296, (3, 24001): 713.155564420994, (3, 24094): 698.209990964756, (3, 24129): 712.6785439439969, (3, 24174): 666.7926253151793, (3, 24235): 688.5980704191915, (3, 24259): 713.0585854329385, (3, 24260): 710.4344629840249, (3, 24261): 708.7091720109929, (3, 24305): 734.4461188797517, (3, 24306): 735.331722627553, (3, 24307): 732.1091465145273, (3, 24308): 774.3711466535854, (3, 24498): 802.8626500731972, (3, 24499): 802.4834331200822, (3, 24500): 800.4372026894423, (3, 24668): 820.2950463329971, (3, 24711): 805.9369173198643, (3, 24756): 803.6423188135749, (3, 24788): 813.425376682911, (3, 24809): 783.4347747581108, (3, 24813): 793.8559986918681, (3, 24821): 790.916146547226, (3, 24825): 791.0092904072281, (3, 24832): 783.0718784183473, (3, 24833): 786.445152132268, (3, 24835): 789.1765899665066, (3, 24837): 796.029866245219, (3, 24840): 781.7869287180615, (3, 24841): 788.577590526818, (3, 24844): 780.9079896368233, (3, 24845): 788.0132959147218, (3, 24846): 782.0508927946368, (3, 24849): 783.3994571885837, (3, 24850): 793.6306551307141, (3, 24863): 754.5235897557261, (3, 24866): 760.8675260348261, (3, 24885): 764.4423803320781, (3, 24886): 762.6907001352615, (3, 24889): 783.9787791296669, (3, 24903): 792.6316573216372, (3, 24909): 776.3293742441309, (3, 24999): 1064.4075852125918, (3, 25019): 1064.9760329721132, (3, 25028): 1059.019281948193, (3, 25137): 228.41851367472265, (3, 25145): 235.9418680744576, (3, 25208): 301.21226582432536, (3, 25233): 290.4694788033626, (3, 25371): 255.59540568961464, (3, 25377): 245.87300892856396, (3, 25828): 239.1665112583774, (3, 25851): 304.46069899281997, (3, 25874): 255.88420828954537, (3, 25898): 216.30713977733242, (3, 25946): 244.99384756949613, (3, 26047): 115.3730658509524, (3, 26066): 258.7128652526673, (3, 26197): 172.20485092113745, (3, 26212): 377.8813348857318, (3, 26253): 395.95088477620806, (3, 26254): 389.44111682489125, (3, 26257): 381.74699755433784, (3, 26258): 391.91605616636974, (3, 26260): 386.78014571567695, (3, 26266): 396.9709829033833, (3, 26267): 390.43335736911763, (3, 26271): 389.7787518362803, (3, 26304): 333.094771728972, (3, 26305): 335.7668070177451, (3, 26363): 233.68516777487994, (3, 26441): 852.6783759211926, (3, 26442): 851.8726626714462, (3, 26450): 841.2312259917237, (3, 26459): 834.8735113543868, (3, 26462): 833.9411591230859, (3, 26467): 864.3646064907565, (3, 26471): 858.5508535270754, (3, 26472): 858.4502143616012, (3, 26473): 858.8778692166568, (3, 26476): 862.1493841487629, (3, 26485): 842.7585673088143, (3, 26493): 845.9239757641797, (3, 26524): 836.0808455351137, (3, 26525): 836.3678267428642, (3, 26556): 854.1769411945393, (3, 26560): 848.6687820984098, (3, 26561): 841.0432114530774, (3, 26564): 852.6130429805105, (3, 26569): 840.9236681644926, (3, 26570): 840.0318514427545, (3, 26573): 844.1402034899235, (3, 26581): 846.089199924742, (3, 26583): 842.4645609613169, (3, 26593): 848.9511901973901, (3, 26837): 868.6110305821101, (3, 26844): 874.5723525386538, (3, 26863): 866.9531440071553, (3, 26893): 886.1709326138863, (3, 26902): 894.4369759909581, (3, 26905): 881.3610858903837, (3, 26912): 889.319847915658, (3, 26921): 875.8190476654406, (3, 26922): 867.2119061084932, (3, 27212): 825.3389762762833, (3, 27218): 813.8874006832888, (3, 27239): 839.452574136192, (3, 27257): 833.5005542501832, (3, 27274): 842.7835116149279, (3, 27279): 842.4450821328295, (3, 27282): 834.4512350229686, (3, 27283): 835.3555412311629, (3, 27285): 847.0986309800925, (3, 27286): 841.8088026113963, (3, 27290): 827.8169572174827, (3, 27295): 821.1423647172242, (3, 27300): 843.7106862267755, (3, 27344): 827.6634134991054, (3, 27366): 837.8582559261963, (3, 27383): 850.2365671424271, (3, 27398): 857.1741655847098, (3, 27406): 848.3728557479152, (3, 27407): 849.8301517158704, (3, 27426): 831.8186306648387, (3, 27432): 799.3417966426737, (3, 27460): 818.6483065369806, (3, 27523): 860.6015553715722, (3, 27545): 980.4584335563145, (3, 27602): 1172.5759253900842, (3, 27606): 1174.758837578625, (3, 27646): 1003.0111745754572, (3, 27667): 1040.3339946225176, (3, 27672): 1041.3589727667904, (3, 27674): 1035.5690600605756, (3, 27688): 1037.2498908497669, (3, 27692): 1048.8930073914162, (3, 27693): 1043.4936277195693, (3, 27705): 1044.2691583444957, (3, 27712): 1047.8273785089546, (3, 27786): 1152.4759101766672, (3, 27790): 1122.4956879218357, (3, 27791): 1119.501899220542, (3, 27795): 1142.6197617253952, (3, 27801): 1120.9516133380173, (3, 27813): 1159.342566996648, (3, 27816): 1150.6475323859684, (3, 27823): 1120.057934688195, (3, 27830): 1140.2420801925712, (3, 27884): 952.7573962997598, (3, 27885): 989.0852096363407, (3, 27896): 966.3826109793137, (3, 27919): 963.7375633809773, (3, 27922): 969.8977582473955, (3, 27930): 956.7581635017125, (3, 27934): 959.1448166625988, (3, 27935): 961.3165827799263, (3, 27948): 1198.4019277832008, (3, 27951): 1192.8961672270252, (3, 28061): 1179.6188051627014, (3, 28290): 1510.1064670504697, (3, 28292): 1522.0274754141194, (3, 28293): 1512.787236782656, (3, 28295): 1512.5510415446938, (3, 28296): 1511.2615987210268, (3, 28297): 1504.0921152877163, (3, 28302): 1504.0493962056623, (3, 28310): 1864.95557017476, (3, 28313): 1876.6516803460147, (3, 28372): 1866.4616711045726, (3, 28398): 1867.9102277693862, (3, 28399): 1866.160961982269, (3, 28400): 1870.4688637022794, (3, 28401): 1857.7445434916472, (3, 28445): 1876.3602423650393, (3, 28475): 1841.1496432060649, (3, 28885): 626.5754573541462, (3, 28886): 621.2471542908017, (3, 28915): 613.2224081028936, (3, 28916): 614.2136827313623, (3, 28917): 610.47091990824, (3, 28921): 633.9476378951522, (3, 28931): 630.4457624770109, (3, 28945): 581.7978643262645, (3, 28982): 596.7219865462694, (3, 29219): 558.0835486311515, (3, 29228): 547.8608032862114, (3, 29246): 595.0191176645737, (3, 29248): 585.1992881534046, (3, 29282): 571.9400513402161, (3, 29290): 611.5874819333069, (3, 29291): 606.0880591121038, (3, 29292): 609.976578092542, (3, 29293): 604.3683194360339, (3, 29294): 605.1037214340582, (3, 29298): 602.453109802569, (3, 29299): 599.6064351544167, (3, 29304): 599.6690926937528, (3, 29317): 589.880231196822, (3, 29323): 589.4244494881503, (3, 29330): 593.6186471902337, (3, 29331): 597.7888350654007, (3, 29344): 539.2877269835836, (3, 29445): 386.81674514467664, (3, 29724): 2562.3755678666625, (3, 29738): 2565.461354815069, (3, 29745): 2557.265580923972, (3, 29748): 2563.1189063870456, (3, 29750): 2569.874104739823, (3, 29759): 2558.386896436454, (3, 29772): 2569.864955356701, (3, 29781): 2567.47573537607, (3, 29784): 2563.764371656525, (3, 29790): 2570.690116086905, (3, 29811): 2565.9538616474624, (3, 29817): 2597.6426848118563, (3, 29818): 2595.380170448361, (3, 29929): 2553.632058478656, (3, 30039): 2582.3139571421357, (3, 30066): 2549.551287065779, (3, 30116): 2453.66482110517, (3, 30238): 2310.609392318231, (3, 30248): 2369.0437263994286, (3, 30260): 2369.5767650555626, (3, 30545): 626.3615382670996, (3, 30733): 568.1191015601008, (3, 30756): 486.1313221903476, (3, 30921): 542.2008366762308, (3, 31079): 840.7647873177087, (3, 31149): 787.5755180334011, (3, 31154): 796.4023347607097, (3, 31160): 786.3798897587143, (3, 31163): 796.2546762552213, (3, 31189): 777.6237314399573, (3, 31215): 786.4733563197981, (3, 31259): 825.1860169603907, (3, 31262): 821.4361611241944, (3, 31430): 868.2944609048778, (3, 31568): 925.3013708903766, (3, 31751): 855.6192557400486, (5, 109): 803.8824274212286, (5, 872): 2352.823970287061, (5, 873): 2361.07109247479, (5, 877): 2358.1284359535325, (5, 879): 2359.3664990122807, (5, 884): 2351.417641148657, (5, 889): 2356.5146979985743, (5, 891): 2348.6486441093853, (5, 892): 2365.728099656645, (5, 894): 2364.625202248503, (5, 896): 2356.4274164537005, (5, 903): 2358.6101128138353, (5, 909): 2344.0713525766873, (5, 910): 2347.232976592958, (5, 912): 2341.810713442748, (5, 913): 2335.8881430236283, (5, 916): 2333.174429600151, (5, 926): 2349.7525815602175, (5, 927): 2346.951153652722, (5, 948): 2345.635170356611, (5, 961): 2349.787451201972, (5, 962): 2350.6253595175467, (5, 963): 2351.5987266602615, (5, 967): 2362.035674873121, (5, 974): 2357.960838386427, (5, 998): 2365.422212631507, (5, 1014): 2543.7938784745447, (5, 1086): 2328.076425762827, (5, 1087): 2326.4181651589342, (5, 1089): 2319.1178288620918, (5, 1090): 2322.652310895387, (5, 1092): 2334.565467880552, (5, 1097): 2325.6004497027334, (5, 1107): 2340.1047929564274, (5, 1387): 1077.593088515072, (5, 1554): 950.7613537990765, (5, 1827): 2731.1539273122203, (5, 1828): 2731.995169252486, (5, 1829): 2733.2792619252364, (5, 1830): 2732.1252303042866, (5, 1831): 2732.836865059042, (5, 1832): 2731.937035992823, (5, 1833): 2732.0109275576124, (5, 1836): 2731.0336224171588, (5, 1841): 2736.3430216405486, (5, 1843): 2734.1343140236445, (5, 1844): 2735.142811030977, (5, 1845): 2732.535139791645, (5, 1847): 2723.947372289919, (5, 1848): 2726.8881553263086, (5, 1849): 2740.694011527815, (5, 1850): 2742.113978173288, (5, 1851): 2729.2064714301355, (5, 1852): 2729.4798729201516, (5, 1854): 2730.8419998466566, (5, 1856): 2723.607982945724, (5, 1857): 2726.719795892002, (5, 1858): 2739.314024409207, (5, 1861): 2733.1451330478244, (5, 1866): 2723.4712168287865, (5, 1867): 2736.445459632694, (5, 1868): 2734.623226873788, (5, 1870): 2734.9744702445537, (5, 1871): 2735.9944739403236, (5, 1875): 2730.6532592394783, (5, 1880): 2725.395827546665, (5, 1882): 2726.3488887628064, (5, 1883): 2742.1612361957523, (5, 1889): 2726.8307487940842, (5, 1893): 2733.33957076795, (5, 1894): 2731.245959095514, (5, 1899): 2724.958204723385, (5, 1900): 2726.4667551125253, (5, 1902): 2736.94109945557, (5, 1905): 2739.658445807245, (5, 1907): 2728.8237213216457, (5, 1910): 2729.735267909628, (5, 1917): 2745.090502092715, (5, 1920): 2728.9704929464915, (5, 1935): 2739.9053090550524, (5, 1937): 2742.207251395878, (5, 1946): 2720.201413269037, (5, 1949): 2722.7186827601063, (5, 1950): 2713.926377710833, (5, 1951): 2718.205644555903, (5, 1952): 2721.609061009368, (5, 1953): 2722.859267295259, (5, 1954): 2720.9373136538147, (5, 1958): 2722.0656726732404, (5, 1960): 2726.441172430682, (5, 1968): 2728.167286566906, (5, 1969): 2740.3018844800713, (5, 1974): 2737.1407802002173, (5, 1975): 2737.1514415846336, (5, 1979): 2730.913658571455, (5, 1980): 2730.569041986738, (5, 1981): 2732.278971104689, (5, 1985): 2733.7202893352096, (5, 1994): 2710.7546597811142, (5, 2011): 2726.2840431290406, (5, 2019): 2747.9322471055348, (5, 2020): 2745.0711206987025, (5, 2029): 2734.331082346832, (5, 2030): 2743.0858910425254, (5, 2032): 2732.6389755171303, (5, 2033): 2738.2816487368855, (5, 2034): 2738.244919814715, (5, 2036): 2727.7384681903272, (5, 2037): 2730.4186098055047, (5, 2038): 2731.055388293669, (5, 2042): 2763.841543813018, (5, 2050): 2736.7131247240463, (5, 2051): 2736.3083325933926, (5, 2053): 2737.1487471885052, (5, 2054): 2740.052215821793, (5, 2066): 2734.155600743633, (5, 2067): 2734.1393387816433, (5, 2071): 2705.245837363204, (5, 2072): 2710.624691439517, (5, 2073): 2695.509328902038, (5, 2074): 2694.8232540738522, (5, 2080): 2685.7694811615397, (5, 2082): 2713.542295828384, (5, 2083): 2716.3190188078565, (5, 2089): 2710.301771756169, (5, 2090): 2712.8782329361975, (5, 2092): 2709.257884702031, (5, 2098): 2689.1768079113704, (5, 2099): 2692.3901440595723, (5, 2101): 2688.679249765775, (5, 2102): 2703.403314540099, (5, 2103): 2698.804078957818, (5, 2104): 2696.3238931116693, (5, 2106): 2718.247142517954, (5, 2112): 2690.7066852115936, (5, 2113): 2705.545476509757, (5, 2114): 2709.224038136159, (5, 2117): 2720.521949957477, (5, 2123): 2695.458731268177, (5, 2124): 2698.4930003365344, (5, 2134): 2690.134765300674, (5, 2138): 2698.948393432237, (5, 2141): 2691.0982492984945, (5, 2148): 2696.6159847643603, (5, 2150): 2683.7660913621316, (5, 2151): 2687.0411717149345, (5, 2152): 2682.1637720751874, (5, 2153): 2697.540788419564, (5, 2154): 2684.9005796754514, (5, 2155): 2683.629972448243, (5, 2156): 2681.163808245431, (5, 2157): 2684.9885096485796, (5, 2160): 2703.7217701215277, (5, 2161): 2681.7498154442783, (5, 2162): 2698.4628421402635, (5, 2163): 2694.1647293612746, (5, 2164): 2693.9415020831943, (5, 2168): 2685.5547719514534, (5, 2172): 2688.8760844192398, (5, 2174): 2686.813058678963, (5, 2178): 2691.5066549562225, (5, 2179): 2689.5827374235746, (5, 2183): 2698.8703374564525, (5, 2185): 2699.130324199777, (5, 2186): 2696.6716179214063, (5, 2190): 2704.1969733716055, (5, 2192): 2699.7939300023613, (5, 2193): 2699.682431634424, (5, 2194): 2695.1848317928257, (5, 2195): 2694.682530428547, (5, 2197): 2700.8295455109906, (5, 2205): 2694.742315237461, (5, 2207): 2686.773673157974, (5, 2208): 2691.259494994595, (5, 2212): 2700.6677467254435, (5, 2214): 2612.47171877269, (5, 2225): 2623.5781737607485, (5, 2231): 2599.399531062119, (5, 2278): 2668.9292954639805, (5, 2284): 2678.328668664294, (5, 2285): 2677.113555662195, (5, 2291): 2659.2887161635886, (5, 2292): 2660.711482783637, (5, 2307): 2672.3522542624555, (5, 2313): 2657.295635505016, (5, 2317): 2653.661688177288, (5, 2319): 2663.940512402998, (5, 2321): 2668.268311090421, (5, 2323): 2667.5482652998307, (5, 2326): 2683.363692936077, (5, 2327): 2679.371303740816, (5, 2329): 2676.6634244190354, (5, 2330): 2673.6176848358477, (5, 2332): 2680.271819089819, (5, 2344): 2669.8523940303603, (5, 2346): 2669.782577212378, (5, 2361): 2667.2190827570894, (5, 2368): 2714.3886048350287, (5, 2374): 2718.8742731850143, (5, 2375): 2720.286269976167, (5, 2377): 2704.851195666052, (5, 2378): 2723.105279257283, (5, 2379): 2723.60791371346, (5, 2380): 2725.042003068821, (5, 2383): 2708.8741481949014, (5, 2385): 2711.202914664997, (5, 2395): 2711.3599013994635, (5, 2397): 2721.834408735884, (5, 2398): 2699.946546448472, (5, 2399): 2705.4173548230606, (5, 2400): 2704.175680337839, (5, 2402): 2713.2740558816586, (5, 2403): 2716.714699395912, (5, 2404): 2717.5547384251204, (5, 2405): 2709.30452192181, (5, 2407): 2715.957969129243, (5, 2408): 2720.0440659399865, (5, 2409): 2711.7893816269025, (5, 2411): 2716.873964587021, (5, 2412): 2715.902608920769, (5, 2413): 2718.7501688617244, (5, 2414): 2714.186432019294, (5, 2422): 2715.889612335244, (5, 2424): 2716.8334513723407, (5, 2426): 2717.5413540247837, (5, 2433): 2711.2018191472266, (5, 2436): 2709.6156016072528, (5, 2437): 2689.5005337112466, (5, 2440): 2693.90118547366, (5, 2445): 2783.5408072906034, (5, 2447): 2772.5531921717698, (5, 2454): 2782.8189245391563, (5, 2455): 2783.3237789144296, (5, 2460): 2751.532752836452, (5, 2461): 2755.471248816597, (5, 2471): 2819.392031633584, (5, 2492): 2753.426102634548, (5, 2511): 2721.463395723801, (5, 2523): 2737.8199859991037, (5, 2525): 2733.0559205361183, (5, 2535): 2740.855245742798, (5, 2537): 2733.838060440981, (5, 2538): 2738.654303087846, (5, 2539): 2736.7155652948704, (5, 2540): 2744.041819930716, (5, 2542): 2749.1646239748193, (5, 2559): 2848.897161030277, (5, 2575): 2840.0048554351265, (5, 2599): 2688.151912832943, (5, 2600): 2722.1832279113223, (5, 2607): 2702.3760723583637, (5, 2627): 2741.126581240966, (5, 2647): 2759.7036677652995, (5, 2674): 2750.183203456551, (5, 2681): 2747.581557158439, (5, 2683): 2756.668486776363, (5, 2686): 2746.2501015013036, (5, 2689): 2867.345726725634, (5, 2690): 2867.928081363043, (5, 2713): 2891.0859162190886, (5, 2714): 2893.0777260144278, (5, 2715): 2896.0585065342143, (5, 2739): 2893.427959212799, (5, 2740): 2874.7319796355196, (5, 2741): 2876.221212537525, (5, 2749): 2889.262850605516, (5, 2750): 2890.2115524255864, (5, 2752): 2892.3446886961824, (5, 2755): 2894.691775374666, (5, 2758): 2893.9897652330114, (5, 2759): 2894.0075246705314, (5, 2769): 2890.5629726812545, (5, 2771): 2879.520391084889, (5, 2779): 2880.3507436000136, (5, 2784): 2846.728997908591, (5, 2800): 2852.608035605059, (5, 2802): 2868.914513461615, (5, 2803): 2867.789902165508, (5, 2804): 2865.8007000635907, (5, 2805): 2871.3947164647393, (5, 2807): 2871.2195929876816, (5, 2809): 2870.084164866713, (5, 2812): 2850.9690106721164, (5, 2814): 2868.99135557442, (5, 2817): 2869.506801597244, (5, 2819): 2871.6340296909943, (5, 2823): 2852.723918905825, (5, 2832): 2875.0848751203794, (5, 2836): 2861.651538824232, (5, 2839): 2871.1874033908844, (5, 2841): 2870.246153631717, (5, 2843): 2869.2732189529734, (5, 2846): 2864.251923330148, (5, 2849): 2877.1600204962597, (5, 2852): 2874.1174614664046, (5, 2853): 2878.559596801783, (5, 2876): 2879.8533449550773, (5, 2877): 2890.618155401303, (5, 2885): 2893.712503818186, (5, 2918): 2873.206174982895, (5, 2921): 2877.836907482044, (5, 2925): 2856.0928396007125, (5, 2926): 2848.812479513085, (5, 2930): 2865.1955868300793, (5, 2931): 2858.0976058820734, (5, 2938): 2873.2563485460673, (5, 2940): 2886.753264126814, (5, 2947): 2870.9104259828123, (5, 2949): 2865.077107297278, (5, 2950): 2867.1555118912975, (5, 2952): 2864.865792308304, (5, 2958): 2864.422313256062, (5, 2959): 2866.6360270799596, (5, 2960): 2871.734023645982, (5, 2961): 2869.28276511762, (5, 2963): 2862.4787509890025, (5, 2968): 2863.931288837774, (5, 2976): 2861.873677098696, (5, 2981): 2818.256756587773, (5, 2982): 2816.9872418287773, (5, 2984): 2814.718954582528, (5, 3003): 2810.722645013311, (5, 3046): 2781.1252284447555, (5, 3050): 2804.4350134623314, (5, 3051): 2806.228011467619, (5, 3053): 2801.228128130707, (5, 3069): 2829.1544893285945, (5, 3071): 2800.025075425527, (5, 3080): 2893.7193702103136, (5, 3199): 2803.2171952138615, (5, 3200): 2797.9274295887385, (5, 3205): 2830.458341869089, (5, 3209): 2800.6819745391062, (5, 3215): 2798.262831217486, (5, 3217): 2791.7648453984043, (5, 3249): 2798.8626824624134, (5, 3263): 2847.9279218712018, (5, 3289): 2814.3785866997696, (5, 3301): 2815.924009957441, (5, 3302): 2813.5885250354872, (5, 3307): 2810.6728132965404, (5, 3310): 2818.720999876688, (5, 3391): 2823.762712338723, (5, 3509): 1768.1064152798692, (5, 3510): 1763.4640181217999, (5, 3511): 1766.547964721898, (5, 3512): 1763.668772074726, (5, 3514): 1764.6374450864744, (5, 3519): 1779.028782032861, (5, 3536): 1776.2820023982915, (5, 3545): 1783.5577960336902, (5, 3548): 1776.4261995999093, (5, 3572): 1778.9285473116056, (5, 3581): 1773.3291683069895, (5, 3583): 1770.1370046989543, (5, 3601): 1787.7568809248476, (5, 3656): 1780.2420064489015, (5, 3669): 1771.1976901239073, (5, 3670): 1775.362356208759, (5, 3695): 1751.5619551495613, (5, 3696): 1754.8510095420465, (5, 3782): 1777.8482788975464, (5, 3792): 1772.7964154641659, (5, 3989): 300.0922074484071, (5, 4008): 324.4408647109586, (5, 4031): 333.1634121580726, (5, 4045): 314.66856671897114, (5, 4144): 306.6126184487749, (5, 4145): 271.89122246134286, (5, 4164): 294.72503732277414, (5, 4168): 282.380836372834, (5, 4173): 278.5226022422133, (5, 4181): 263.45500973842746, (5, 4228): 260.4244178496351, (5, 4248): 239.39041620589688, (5, 4254): 60.65722525070469, (5, 4260): 65.18839740010479, (5, 4262): 71.59483179991345, (5, 4273): 72.16587171730752, (5, 4319): 39.402822704129, (5, 4326): 40.26936238678442, (5, 4328): 37.48166112121465, (5, 4334): 38.46237477101797, (5, 4335): 41.41474997236869, (5, 4372): 818.3350761123663, (5, 4413): 869.2518297186762, (5, 4434): 811.5746886948549, (5, 4447): 798.1775473088909, (5, 4452): 814.6503856098643, (5, 4463): 882.5301491133197, (5, 4465): 876.8008841164371, (5, 4619): 926.3956665268547, (5, 4645): 920.7415776742257, (5, 4657): 926.9884768062052, (5, 4666): 931.9259502087948, (5, 4676): 933.6099299136623, (5, 4678): 930.8540279932233, (5, 4689): 937.567203743276, (5, 4704): 948.8560086260924, (5, 4726): 1125.2445227126386, (5, 4727): 1122.512135151559, (5, 4730): 1116.796781832314, (5, 4731): 1121.2274977650252, (5, 4734): 1108.243657868339, (5, 4735): 1108.0602061267582, (5, 4736): 1111.4545899035509, (5, 4737): 1109.7092894557363, (5, 4738): 1112.009330844803, (5, 4756): 1116.0173144597968, (5, 4760): 1090.575372270512, (5, 4761): 1087.3744198851684, (5, 4762): 1089.7412388700925, (5, 4765): 1093.3299345450564, (5, 4773): 1128.3040371977315, (5, 4774): 1129.6976581932915, (5, 4790): 1125.9113074482996, (5, 4795): 1122.5621271402972, (5, 4799): 1132.9078608153388, (5, 4801): 1143.8651654788034, (5, 4804): 1118.6892744456038, (5, 4805): 1115.9920338614431, (5, 4806): 1134.3106997153743, (5, 4815): 1135.0696457731106, (5, 4816): 1140.156954398808, (5, 4817): 1145.9094277328577, (5, 4826): 1140.4887831546175, (5, 4830): 1138.5016302649317, (5, 4839): 1098.7161275490907, (5, 4840): 1103.0540995143053, (5, 4841): 1098.8754377487983, (5, 4846): 1096.2407720012584, (5, 4848): 1099.4718216394494, (5, 4850): 1102.5910107867305, (5, 4871): 1053.5952487355194, (5, 4883): 1081.9078846158866, (5, 4900): 1061.8803564107604, (5, 4901): 1061.6185763714393, (5, 4917): 1003.5167709760474, (5, 4931): 991.5105224953462, (5, 4944): 1001.9686167898273, (5, 4956): 996.6168701107451, (5, 4958): 1002.0655506371245, (5, 4959): 1003.7877365125341, (5, 4961): 996.6650480822229, (5, 4966): 997.0814623130841, (5, 5207): 984.8305717029585, (5, 5272): 654.3589551456289, (5, 5283): 656.7161116205277, (5, 5287): 674.5504500158655, (5, 5289): 676.2393903199094, (5, 5293): 641.345299263456, (5, 5295): 646.122493849802, (5, 5296): 654.5417711957609, (5, 5298): 659.1963593651241, (5, 5303): 668.0660481603039, (5, 5305): 669.662515169175, (5, 5306): 680.2459878250241, (5, 5307): 669.5249822174693, (5, 5308): 673.1754283971542, (5, 5313): 662.5212605557336, (5, 5314): 660.423045000423, (5, 5317): 678.6675712962415, (5, 5319): 668.2103229910393, (5, 5324): 660.6762695748984, (5, 5326): 655.3688180931343, (5, 5348): 687.0675003549062, (5, 5351): 700.0724841915601, (5, 5399): 689.7915709715422, (5, 5413): 721.0693031442933, (5, 5422): 682.4665124275793, (5, 5445): 681.7779825054771, (5, 5448): 680.2139095773606, (5, 5456): 688.7798113832686, (5, 5467): 692.6210676736273, (5, 5624): 653.0604157553488, (5, 5671): 596.8638250531146, (5, 5672): 591.3333907634461, (5, 5797): 667.7584837612634, (5, 5871): 805.160982588002, (5, 5976): 778.5735199736245, (5, 6118): 2330.50022525446, (5, 6248): 2430.6150436766698, (5, 6345): 737.0235706448134, (5, 6352): 760.10265403035, (5, 6354): 730.9270326365555, (5, 6359): 727.1938844472996, (5, 6376): 758.620133341959, (5, 6378): 733.7519710653493, (5, 6381): 729.6668149227542, (5, 6383): 741.582822915849, (5, 6396): 735.880130697959, (5, 6399): 737.7562934804923, (5, 6408): 758.4173582932747, (5, 6409): 745.4863648648529, (5, 6419): 779.4499439351366, (5, 6422): 753.711987089249, (5, 6423): 755.4517830451506, (5, 6424): 730.870390994498, (5, 6439): 734.6381126405468, (5, 6464): 740.3799006769376, (5, 6465): 743.3303034388116, (5, 6469): 741.9385115935518, (5, 6470): 743.6991970661578, (5, 6472): 719.7031389344738, (5, 6480): 721.0173767813851, (5, 6486): 704.3155435705378, (5, 6497): 709.6831440113893, (5, 6503): 735.3102630308332, (5, 6508): 735.5506604472099, (5, 6509): 730.2862358914363, (5, 6521): 716.7419694502671, (5, 6544): 716.4606023762805, (5, 6552): 746.3013985237044, (5, 6553): 749.6447587962025, (5, 6554): 753.0719986113281, (5, 6578): 740.9961503882403, (5, 6582): 741.5834564894872, (5, 6601): 739.0329506401836, (5, 6609): 713.8972549269196, (5, 6610): 712.4495407117175, (5, 6611): 713.022340214118, (5, 6614): 715.5832632874318, (5, 6615): 714.4943691217125, (5, 6616): 709.2860328819891, (5, 6617): 711.4172232215363, (5, 6618): 704.7789357680548, (5, 6619): 717.8100409210655, (5, 6620): 708.4691472481388, (5, 6621): 711.2407988439066, (5, 6622): 711.0656453096353, (5, 6623): 715.0151963233645, (5, 6624): 716.7995851612201, (5, 6625): 717.7660372017223, (5, 6626): 718.3308252753849, (5, 6627): 717.0297082284407, (5, 6628): 708.3441144380628, (5, 6629): 715.0635035129844, (5, 6630): 721.5650843342361, (5, 6632): 715.7762309331017, (5, 6634): 724.2037486269536, (5, 6635): 712.6866079213244, (5, 6636): 708.8614314491523, (5, 6637): 718.9953265594062, (5, 6638): 720.4372036412179, (5, 6639): 716.2396373672856, (5, 6640): 720.3518145044112, (5, 6641): 710.7557410767606, (5, 6642): 719.8434533293295, (5, 6643): 719.2553011431858, (5, 6645): 717.0337231961217, (5, 6646): 706.4053181535118, (5, 6647): 719.2527369274144, (5, 6653): 714.8766687951208, (5, 6655): 716.4766794547124, (5, 6658): 724.1080673572366, (5, 6662): 719.4597235900615, (5, 6819): 878.2341199118284, (5, 6996): 817.1357424113592, (5, 7059): 778.5076603070806, (5, 7187): 853.0823608568052, (5, 7304): 926.6114659665268, (5, 7528): 820.8998791930869, (5, 7720): 591.316446054633, (5, 7793): 596.7507033517229, (5, 7807): 593.2705505139634, (5, 7808): 598.2017053270404, (5, 7831): 687.8842518926172, (5, 7850): 654.2816908800602, (5, 7852): 663.8290810058738, (5, 8012): 602.9929960116796, (5, 8125): 589.6431232012999, (5, 8208): 521.0007242022855, (5, 8392): 653.5827166730924, (5, 8651): 1064.007773103958, (5, 9088): 904.6265145835031, (5, 9443): 1152.458535223655, (5, 9444): 1147.3491366033854, (5, 9828): 1330.5567027376903, (5, 9868): 1325.6252887139126, (5, 10180): 589.4978190123842, (5, 10256): 504.7914078140245, (5, 10276): 536.2367005414486, (5, 10378): 507.59600102112444, (5, 10676): 656.4663074529213, (5, 10714): 723.2462230525504, (5, 10730): 684.1503718799567, (5, 10862): 1182.4517820427604, (5, 10881): 1178.9812026630398, (5, 10883): 1181.698789753884, (5, 10885): 1182.6328605646113, (5, 10891): 1185.9798819646833, (5, 10909): 1180.7120550038965, (5, 10911): 1174.508687515531, (5, 10913): 1177.155606194304, (5, 10915): 1174.2463496751166, (5, 10919): 1171.285862356902, (5, 11037): 1266.0549520155773, (5, 11039): 1252.7663622376917, (5, 11516): 653.194872603967, (5, 11856): 37.66477236461416, (5, 11857): 49.61449281627272, (5, 11861): 43.82608358698269, (5, 11881): 32.761612866472234, (5, 11902): 44.64908734521278, (5, 11911): 42.01370984099707, (5, 11914): 41.91061959450375, (5, 11922): 34.15196597075156, (5, 11924): 29.36896182777283, (5, 11926): 32.44613367882386, (5, 11950): 17.664727050015426, (5, 11963): 10.60788539461579, (5, 11983): 14.316481604390862, (5, 11985): 15.266850620977864, (5, 12009): 6.956148290822549, (5, 12010): 6.247108748970781, (5, 12018): 5.61043119679681, (5, 12020): 1.4441892722775218, (5, 12021): 2.748436769524235, (5, 12024): 11.742077539247814, (5, 12025): 8.176150411133344, (5, 12027): 5.460882647818341, (5, 12031): 8.11383272606851, (5, 12032): 4.303427171984664, (5, 12035): 9.61174673187271, (5, 12041): 24.82040928208167, (5, 12045): 141.317837643194, (5, 12145): 74.5497176715186, (5, 12275): 332.6498909742163, (5, 12294): 330.84598832854334, (5, 12358): 398.8465407537505, (5, 12463): 435.92607011288237, (5, 12465): 436.00310437440174, (5, 12482): 435.162502584108, (5, 12503): 436.46331975442257, (5, 12506): 439.10582655363925, (5, 12549): 420.2151194595962, (5, 12559): 420.7738217853052, (5, 12569): 427.6259067953549, (5, 12572): 429.3544455815295, (5, 12574): 424.29405973761925, (5, 12576): 421.01981436972596, (5, 12591): 413.24031975643715, (5, 12608): 425.4169119984294, (5, 12696): 393.1723489860153, (5, 12710): 400.36748311741576, (5, 12728): 401.9653874944985, (5, 12766): 467.84508854572607, (5, 12771): 468.37112986274354, (5, 12790): 472.54479284028247, (5, 12795): 484.8700403851154, (5, 12797): 505.0469571589013, (5, 12798): 499.72649797470564, (5, 12811): 474.6885743217861, (5, 12830): 486.81455446907, (5, 12848): 474.7557112790372, (5, 12850): 468.10827872376996, (5, 12852): 485.67579488866454, (5, 12854): 489.5706460189098, (5, 12859): 468.8642334810316, (5, 12861): 493.6990314489123, (5, 12865): 473.5093720178802, (5, 12866): 473.10475885007753, (5, 12867): 467.6468217715048, (5, 12874): 470.60219822893265, (5, 12875): 466.71181272358814, (5, 12881): 481.2347822394503, (5, 12883): 476.2467481733103, (5, 12885): 464.7790192337932, (5, 12888): 476.8803848716213, (5, 12889): 476.43412930333557, (5, 12892): 470.71026682763454, (5, 12893): 478.3211700118064, (5, 12896): 474.3993957925607, (5, 12906): 477.7543697420925, (5, 13018): 556.7089017634138, (5, 13071): 567.1001725654089, (5, 13131): 558.0173581186833, (5, 13146): 524.1081879047985, (5, 13159): 609.2215746359263, (5, 13193): 560.6472423518723, (5, 13198): 596.3100954327399, (5, 13292): 535.7245891428864, (5, 13296): 506.07500492858406, (5, 13406): 648.0078826969407, (5, 13407): 651.3448371380163, (5, 13417): 669.1893063286864, (5, 13418): 666.3931840059909, (5, 13438): 633.6300614926621, (5, 13442): 624.556796571455, (5, 13443): 629.2994614746694, (5, 13764): 1097.938053449167, (5, 13766): 1092.1224104482326, (5, 13771): 1102.7179079829734, (5, 13783): 1094.7739708012452, (5, 13784): 1083.6687271425124, (5, 13792): 1121.3996602661346, (5, 13824): 1099.733116666323, (5, 14017): 1038.6625439918223, (5, 14870): 1064.9064643986173, (5, 14997): 882.6209383327576, (5, 15000): 882.3626517692828, (5, 15003): 878.6991432911177, (5, 15006): 868.2097756117959, (5, 15007): 864.1368159064008, (5, 15056): 865.6049603877553, (5, 15063): 869.4710861295905, (5, 15069): 871.2900866210466, (5, 15076): 863.6825498702204, (5, 15086): 876.2253661608547, (5, 15087): 880.9974287192861, (5, 15111): 893.0630022983572, (5, 15116): 886.1525660078096, (5, 15722): 994.853326711441, (5, 15998): 1080.5099739836573, (5, 16073): 1975.1182370485926, (5, 16939): 2473.4697883184635, (5, 16940): 2467.4150553070017, (5, 16951): 2474.4563160499356, (5, 16963): 2475.002130619181, (5, 16965): 2482.30499133556, (5, 16969): 2480.608869171521, (5, 16970): 2477.617084316813, (5, 16971): 2471.031659124046, (5, 16973): 2470.64353495404, (5, 16974): 2485.292281294737, (5, 16976): 2478.09290790934, (5, 16978): 2473.2625386221134, (5, 16980): 2480.4793438170987, (5, 16982): 2485.2966858787904, (5, 17045): 2689.5998347367695, (5, 17048): 2698.130299739261, (5, 17304): 191.88403310898764, (5, 17305): 195.49023788060055, (5, 17330): 196.5036818472766, (5, 17334): 183.78050252213083, (5, 17343): 203.0083317477574, (5, 17345): 191.06434163715932, (5, 17347): 200.9740784770076, (5, 17351): 174.6159062138547, (5, 17372): 185.82912442643044, (5, 17373): 201.4885389341957, (5, 17377): 203.1897284339973, (5, 17382): 194.57313260766023, (5, 17383): 193.67799946309322, (5, 17389): 189.19718600328895, (5, 17400): 196.78526670060472, (5, 17401): 195.46768891929025, (5, 17402): 197.99950398746898, (5, 17403): 199.45568835708968, (5, 17440): 200.1437614634792, (5, 17455): 206.45112236527527, (5, 17491): 212.97699442800524, (5, 17507): 162.68144737800776, (5, 17509): 165.977505877172, (5, 17590): 180.5270277940239, (5, 17615): 110.18362320508925, (5, 17642): 117.8440699388163, (5, 17643): 119.56145566160059, (5, 17668): 108.78511510916944, (5, 17721): 88.62464005449586, (5, 17754): 137.80173001812352, (5, 17769): 157.59654263270215, (5, 17776): 150.25245122999928, (5, 17804): 164.73751230899936, (5, 17809): 169.75171684845427, (5, 17824): 163.37921465059515, (5, 17837): 166.5818756716506, (5, 17838): 171.06029946128706, (5, 17862): 169.69995711488724, (5, 17866): 177.36843945747896, (5, 17872): 163.97328440956557, (5, 17873): 159.3719395408397, (5, 17881): 167.1878255300983, (5, 17947): 1973.4098564543647, (5, 17951): 1962.282616146408, (5, 17953): 1959.9394744842323, (5, 17954): 1960.575755945234, (5, 17959): 1971.4963359307328, (5, 17963): 1967.9506787845855, (5, 18000): 1910.7297432775517, (5, 18001): 1912.6730161489154, (5, 18111): 2062.7601842927725, (5, 18148): 1774.063780557795, (5, 18166): 1884.7195239806947, (5, 18189): 1990.1079585359084, (5, 18239): 201.06853529188945, (5, 18240): 201.78962716058706, (5, 18245): 201.89640862450597, (5, 18247): 201.72755753025774, (5, 18251): 202.8254003454924, (5, 18256): 204.92666561134112, (5, 18258): 204.24243225024964, (5, 18259): 204.8734721974907, (5, 18260): 205.91198716725427, (5, 18262): 207.30197673786097, (5, 18263): 205.67301077461198, (5, 18264): 206.6523383355448, (5, 18266): 208.34768773692656, (5, 18267): 209.19842464181966, (5, 18268): 209.9163916090859, (5, 18269): 211.69992225169634, (5, 18275): 210.86187234787076, (5, 18285): 206.00896053927573, (5, 18308): 187.55336554763687, (5, 18313): 183.45353999365247, (5, 18314): 187.6891164364514, (5, 18315): 209.39938935383137, (5, 18316): 210.34384675001448, (5, 18317): 211.2441546960744, (5, 18320): 210.5456652184381, (5, 18321): 211.51998941322572, (5, 18322): 212.72017874150774, (5, 18324): 212.1800771528357, (5, 18325): 214.43729133387725, (5, 18326): 213.54740569396853, (5, 18327): 212.97015477186372, (5, 18329): 214.28469736047506, (5, 18330): 216.43883536759742, (5, 18331): 214.4083174630815, (5, 18332): 212.86984211015337, (5, 18333): 215.2560154326384, (5, 18336): 212.40794225708706, (5, 18337): 212.50614136472853, (5, 18403): 217.38557167383482, (5, 18432): 224.4514914210916, (5, 18451): 218.65694745322247, (5, 18466): 215.13958176407792, (5, 18481): 207.2071702451987, (5, 18483): 207.94259945293265, (5, 18484): 206.12977036446202, (5, 18485): 199.9297993143361, (5, 18486): 200.73066626207788, (5, 18487): 196.93526411000698, (5, 18489): 202.81337316507202, (5, 18490): 203.78683587757467, (5, 18491): 205.16727921498673, (5, 18492): 194.58819613316342, (5, 18493): 199.39438909686987, (5, 18494): 202.8462447374994, (5, 18495): 202.65220063181107, (5, 18496): 201.79344108340226, (5, 18497): 195.4063608010105, (5, 18498): 198.98972279870583, (5, 18499): 201.40234974351682, (5, 18501): 198.38444416291844, (5, 18502): 196.75654560291898, (5, 18503): 196.38422824554291, (5, 18504): 203.25047782098667, (5, 18506): 196.57789886979234, (5, 18507): 194.62530362041315, (5, 18508): 200.36712352315595, (5, 18509): 199.71845719965958, (5, 18510): 195.41771276939588, (5, 18511): 198.42790664097794, (5, 18512): 197.94022782106316, (5, 18515): 202.37451600218054, (5, 18516): 200.1661634718646, (5, 18517): 197.1093138649729, (5, 18518): 202.0537349779442, (5, 18519): 203.99937044233087, (5, 18520): 200.77530330740555, (5, 18522): 211.87010116763142, (5, 18523): 211.39225169818968, (5, 18532): 212.3169614862241, (5, 18535): 209.5967097404418, (5, 18537): 208.10096156172187, (5, 18539): 207.9938197174356, (5, 18540): 207.7274020291145, (5, 18541): 208.10767095645392, (5, 18542): 208.42827825873616, (5, 18543): 206.53263408035164, (5, 18546): 206.08442303726216, (5, 18555): 208.41269107148767, (5, 18556): 208.31721360111544, (5, 18565): 211.09050551850817, (5, 18567): 210.27096010733123, (5, 18568): 209.6279497842054, (5, 18577): 219.36895080370684, (5, 18583): 219.7350878950845, (5, 18605): 224.25875693503673, (5, 18608): 208.11473107721932, (5, 18616): 233.34509554354744, (5, 18618): 240.1916998765328, (5, 18625): 242.48231703199704, (5, 18645): 237.8542666715335, (5, 18646): 237.80722403656364, (5, 18653): 226.17263296449153, (5, 18654): 232.29729751614505, (5, 18655): 227.16708792294577, (5, 18666): 261.8926727662585, (5, 18837): 336.690997849669, (5, 18974): 240.9717805243508, (5, 18999): 257.98432231538544, (5, 19000): 259.9072247713673, (5, 19174): 295.46757727847967, (5, 19342): 327.1733103213534, (5, 19455): 234.3718230216862, (5, 19555): 311.39114533982394, (5, 19564): 340.0870820387138, (5, 19573): 335.7378320059791, (5, 19586): 331.7707576072276, (5, 19605): 325.48251681785433, (5, 19611): 327.0366329052804, (5, 19614): 317.4190457397277, (5, 19641): 312.9894571198468, (5, 19702): 324.0024291502223, (5, 19713): 321.2923954068414, (5, 19731): 279.9551259551918, (5, 19819): 256.85466560154714, (5, 19893): 346.0081226380162, (5, 19899): 362.1037057299025, (5, 19929): 342.07592088824833, (5, 19951): 353.2283367582111, (5, 19962): 356.6646993007756, (5, 19970): 328.0964004834997, (5, 19971): 335.0054693620164, (5, 19972): 339.5938328882256, (5, 19975): 334.6579772199829, (5, 19978): 324.5740792192271, (5, 19987): 319.9993425849903, (5, 19989): 314.9293873003853, (5, 20039): 318.6871858085214, (5, 20043): 314.45802727050136, (5, 20047): 306.38644967286376, (5, 20052): 306.18533675089446, (5, 20054): 309.7547296018299, (5, 20085): 303.4631531451635, (5, 20104): 305.51116893847944, (5, 20132): 302.05791658859965, (5, 20203): 407.87711207028025, (5, 20280): 427.929234796998, (5, 20285): 436.37015839629026, (5, 20290): 424.01130932615416, (5, 20297): 422.5094505004919, (5, 20309): 378.15530904446166, (5, 20453): 372.8568067608999, (5, 20485): 418.85304772883654, (5, 20520): 417.68535927687986, (5, 20526): 437.8969588442893, (5, 20698): 1344.8767357694549, (5, 20868): 1555.3133992168214, (5, 21042): 412.7963621428416, (5, 21057): 370.2486915153814, (5, 21066): 390.3444031591752, (5, 21075): 399.42259740378364, (5, 21093): 408.8434612752151, (5, 21098): 377.691192853961, (5, 21127): 408.8279743429166, (5, 21130): 400.39415862552806, (5, 21144): 402.3491758468587, (5, 21146): 411.6397635012297, (5, 21147): 403.3620084710483, (5, 21148): 395.59819431690545, (5, 21153): 419.5544030102609, (5, 21293): 340.7140005980314, (5, 21426): 380.60252683863183, (5, 21442): 353.64248720010096, (5, 21451): 351.11245002647615, (5, 21466): 363.49550867443, (5, 21469): 356.76058348929865, (5, 21471): 367.02935262901013, (5, 21473): 360.8098642784025, (5, 21475): 365.6619895142844, (5, 21482): 354.7363033862301, (5, 21484): 354.9542733226646, (5, 21488): 359.4956474790756, (5, 21494): 362.79190432123625, (5, 21498): 358.47936705723873, (5, 21500): 363.1146914567064, (5, 21514): 340.9077705603897, (5, 21537): 358.62901946791703, (5, 21662): 329.2161230256854, (5, 21691): 354.68149358282324, (5, 21757): 416.3243198524516, (5, 21777): 496.82941731519884, (5, 21778): 503.6053283914338, (5, 21779): 500.3119683258488, (5, 21790): 488.76017557411217, (5, 21802): 489.98992480641107, (5, 21824): 483.5272867067363, (5, 21874): 499.27745436848573, (5, 21879): 504.57735029336857, (5, 21983): 472.33204379979884, (5, 22002): 400.8341498230771, (5, 22132): 459.5414946726772, (5, 22261): 1397.5040735189516, (5, 22298): 1384.5318110780581, (5, 22339): 1467.6862800851254, (5, 22508): 1262.6998014219985, (5, 22841): 2787.7306736652827, (5, 22842): 2788.018612575703, (5, 22874): 2772.3897590697975, (5, 22941): 2773.217984174534, (5, 22956): 2783.5131844522803, (5, 22960): 2785.8743557860057, (5, 22968): 2799.1827993811225, (5, 22970): 2801.477820124311, (5, 22974): 2808.4590097047326, (5, 22980): 2820.5859561289712, (5, 23025): 2822.0763676853276, (5, 23028): 2819.904397325124, (5, 23081): 2843.354614438714, (5, 23104): 2825.2755533938894, (5, 23147): 2711.524813809297, (5, 23298): 220.082140028138, (5, 23376): 236.72673725084167, (5, 23381): 238.39323222017688, (5, 23529): 200.1713615495384, (5, 23556): 211.4327327298616, (5, 23718): 240.90302848846423, (5, 24001): 144.1729914235697, (5, 24094): 85.75189273268154, (5, 24129): 78.98715898723789, (5, 24174): 84.07717313470864, (5, 24235): 47.33106884563662, (5, 24259): 55.738439683372235, (5, 24260): 53.71729026405122, (5, 24261): 56.009603049801086, (5, 24305): 65.27298438018782, (5, 24306): 63.92324692133426, (5, 24307): 63.49910377863494, (5, 24308): 162.77667403809855, (5, 24498): 128.3402565723657, (5, 24499): 127.7299203359115, (5, 24500): 126.52863287638584, (5, 24668): 164.74510125380812, (5, 24711): 126.62057590347843, (5, 24756): 124.92284085594954, (5, 24788): 134.42147534741426, (5, 24809): 104.71043035267405, (5, 24813): 114.90973856061174, (5, 24821): 111.98164878158933, (5, 24825): 112.31735181808449, (5, 24832): 104.1588635262548, (5, 24833): 107.63166291558414, (5, 24835): 110.55266128820757, (5, 24837): 117.37388132596779, (5, 24840): 102.95095254583788, (5, 24841): 109.70377889327982, (5, 24844): 102.2144218017943, (5, 24845): 108.93520985194803, (5, 24846): 103.71064163206373, (5, 24849): 105.21604737638668, (5, 24850): 114.85949944187085, (5, 24863): 75.86072760571187, (5, 24866): 81.92867836425485, (5, 24885): 85.02601966357, (5, 24886): 83.21511593002303, (5, 24889): 104.61075362009262, (5, 24903): 113.36081238558835, (5, 24909): 98.88406168721045, (5, 24999): 385.7088220990168, (5, 25019): 385.76845483446556, (5, 25028): 380.40939232898734, (5, 25137): 512.0414784373028, (5, 25145): 508.58896765973407, (5, 25208): 557.9026192206117, (5, 25233): 563.0980991003373, (5, 25371): 460.8944107292442, (5, 25377): 456.18063900013476, (5, 25828): 697.8237151734435, (5, 25851): 727.2957451693567, (5, 25874): 686.5526000208853, (5, 25898): 686.2194787238184, (5, 25946): 701.4105182226743, (5, 26047): 653.121077584856, (5, 26066): 441.41976197619044, (5, 26197): 559.4844574581302, (5, 26212): 915.9492576075784, (5, 26253): 937.8022648749591, (5, 26254): 928.1908659295229, (5, 26257): 924.6809682949092, (5, 26258): 934.6068935753733, (5, 26260): 929.1915030558217, (5, 26266): 928.2388916396808, (5, 26267): 923.2230545976631, (5, 26271): 924.1396854088887, (5, 26304): 843.1926114524558, (5, 26305): 840.9459055687261, (5, 26363): 737.5388014909829, (5, 26441): 1426.1983249958525, (5, 26442): 1424.2563118295711, (5, 26450): 1413.275315554524, (5, 26459): 1411.1780889608444, (5, 26462): 1412.169443396082, (5, 26467): 1444.1787282277735, (5, 26471): 1435.8238137706533, (5, 26472): 1435.0548769980555, (5, 26473): 1434.8622895302965, (5, 26476): 1431.5736364477395, (5, 26485): 1417.2260358088731, (5, 26493): 1418.1990260202695, (5, 26524): 1416.4269158883376, (5, 26525): 1415.5046509197073, (5, 26556): 1431.4361551012137, (5, 26560): 1429.3585454559784, (5, 26561): 1422.2030028092531, (5, 26564): 1428.7631507558851, (5, 26569): 1420.854352333906, (5, 26570): 1418.4910388670494, (5, 26573): 1420.810705571748, (5, 26581): 1421.068114153616, (5, 26583): 1418.3615263650813, (5, 26593): 1421.7946231159385, (5, 26837): 1446.8624554437083, (5, 26844): 1453.9368751246475, (5, 26863): 1439.7909231872868, (5, 26893): 1460.6521335746293, (5, 26902): 1470.2994448382817, (5, 26905): 1459.4174701541258, (5, 26912): 1467.3037189105185, (5, 26921): 1449.7055904969402, (5, 26922): 1432.2120246197471, (5, 27212): 1472.3802858997346, (5, 27218): 1462.636759170871, (5, 27239): 1486.5867969091573, (5, 27257): 1479.632622233265, (5, 27274): 1489.6168277290703, (5, 27279): 1488.4180579189099, (5, 27282): 1480.152475309339, (5, 27283): 1482.7160891543247, (5, 27285): 1493.5751898109663, (5, 27286): 1486.6299645485874, (5, 27290): 1473.1468959226795, (5, 27295): 1467.5139011989304, (5, 27300): 1490.9009019610526, (5, 27344): 1470.4109649222314, (5, 27366): 1480.1210019258608, (5, 27383): 1495.0507408854924, (5, 27398): 1504.2585316176742, (5, 27406): 1495.775751143998, (5, 27407): 1497.931224033835, (5, 27426): 1484.6812672286696, (5, 27432): 1449.6398918803154, (5, 27460): 1471.25866934695, (5, 27523): 1488.7077061791829, (5, 27545): 1628.7463434791516, (5, 27602): 1819.4735479945243, (5, 27606): 1822.5036107939834, (5, 27646): 1632.3277781046675, (5, 27667): 1670.205904660163, (5, 27672): 1671.9122835270766, (5, 27674): 1665.6289814853278, (5, 27688): 1669.935733330089, (5, 27692): 1678.784389608617, (5, 27693): 1673.172433124185, (5, 27705): 1673.1934751738631, (5, 27712): 1676.2218534011681, (5, 27786): 1816.5093837150891, (5, 27790): 1790.96130666085, (5, 27791): 1788.5536022821216, (5, 27795): 1806.210848855342, (5, 27801): 1787.56246461384, (5, 27813): 1822.833458942109, (5, 27816): 1815.084628743038, (5, 27823): 1786.8176207864665, (5, 27830): 1805.7400729022283, (5, 27884): 1572.5373742055515, (5, 27885): 1616.9318987872186, (5, 27896): 1589.9083277922834, (5, 27919): 1587.7373117831935, (5, 27922): 1593.7342366257478, (5, 27930): 1578.8682167145055, (5, 27934): 1580.8536069211293, (5, 27935): 1582.4354817370395, (5, 27948): 1814.1689093080277, (5, 27951): 1820.054487527069, (5, 28061): 1667.4383047175033, (5, 28290): 2054.3399330972743, (5, 28292): 2062.7483586161375, (5, 28293): 2056.010461535402, (5, 28295): 2052.8915542870163, (5, 28296): 2054.0685704273765, (5, 28297): 2049.8953843840286, (5, 28302): 2047.2879126231896, (5, 28310): 2187.3341596775854, (5, 28313): 2192.896151219707, (5, 28372): 2195.1176658985833, (5, 28398): 2195.675212126725, (5, 28399): 2192.999828728987, (5, 28400): 2197.197208070257, (5, 28401): 2186.316689844797, (5, 28445): 2188.668274469276, (5, 28475): 2178.610177778695, (5, 28885): 53.230131431102286, (5, 28886): 58.49330390778336, (5, 28915): 68.3178888160401, (5, 28916): 66.29014632549335, (5, 28917): 70.06837228818875, (5, 28921): 46.354141530386684, (5, 28931): 50.115646840700826, (5, 28945): 101.59387444404473, (5, 28982): 85.36093606903454, (5, 29219): 149.37007657878112, (5, 29228): 150.13796758821314, (5, 29246): 209.39395039025783, (5, 29248): 222.09916899327905, (5, 29282): 208.77621386391857, (5, 29290): 201.864548619773, (5, 29291): 202.92528086233048, (5, 29292): 203.77921597813616, (5, 29293): 198.41449568520113, (5, 29294): 208.17140289180344, (5, 29298): 202.27259681961957, (5, 29299): 205.35832216598652, (5, 29304): 192.79590122718773, (5, 29317): 176.90244814052343, (5, 29323): 175.32331775273047, (5, 29330): 183.35884181397608, (5, 29331): 184.48646526498695, (5, 29344): 177.68518137464318, (5, 29445): 295.19396583609245, (5, 29724): 2744.9504045706085, (5, 29738): 2748.212540103708, (5, 29745): 2738.095486806069, (5, 29748): 2736.9122120125207, (5, 29750): 2740.9454103961266, (5, 29759): 2732.816756302386, (5, 29772): 2744.825242650914, (5, 29781): 2742.115184256055, (5, 29784): 2741.375083347479, (5, 29790): 2744.187986286173, (5, 29811): 2735.9827378705527, (5, 29817): 2750.0213050453513, (5, 29818): 2747.325474476444, (5, 29929): 2738.847682231305, (5, 30039): 2789.544138625951, (5, 30066): 2766.6813962976225, (5, 30116): 2649.6071340865988, (5, 30238): 2476.2326376629558, (5, 30248): 2569.9293121636665, (5, 30260): 2572.577742263188, (5, 30545): 85.62312756193535, (5, 30733): 262.56461826667385, (5, 30756): 309.8417792699553, (5, 30921): 222.7211024721764, (5, 31079): 767.3729397983549, (5, 31149): 755.9330410169805, (5, 31154): 760.2060563224572, (5, 31160): 756.3964117495931, (5, 31163): 762.3269193985841, (5, 31189): 811.1400727417655, (5, 31215): 811.8413499859017, (5, 31259): 838.070655602906, (5, 31262): 842.183799201794, (5, 31430): 778.8011336876042, (5, 31568): 961.0650133895489, (5, 31751): 806.379198838064, (6, 109): 404.80020775688746, (6, 872): 1456.8690087368475, (6, 873): 1465.2382070870879, (6, 877): 1464.0449164537165, (6, 879): 1465.47571296639, (6, 884): 1461.4421564274369, (6, 889): 1465.7514856764715, (6, 891): 1458.1528469473894, (6, 892): 1471.5604052058143, (6, 894): 1469.7072445698432, (6, 896): 1458.4121779951815, (6, 903): 1466.5851485722817, (6, 909): 1445.9497165436053, (6, 910): 1447.492863026134, (6, 912): 1442.3862128529047, (6, 913): 1437.4289534055813, (6, 916): 1432.6866572652725, (6, 926): 1447.86767118341, (6, 927): 1444.6555085217262, (6, 948): 1454.8095578667856, (6, 961): 1451.7869388242746, (6, 962): 1451.4769785490655, (6, 963): 1451.535843172291, (6, 967): 1469.3299030958897, (6, 974): 1469.3994470267057, (6, 998): 1474.2426598232387, (6, 1014): 1635.2875506171858, (6, 1086): 1384.2761689588806, (6, 1087): 1376.9057062296265, (6, 1089): 1372.5177114948765, (6, 1090): 1376.5509934222237, (6, 1092): 1388.5893843563722, (6, 1097): 1380.6544626425946, (6, 1107): 1390.6019679583028, (6, 1387): 385.01190000174563, (6, 1554): 439.23359393598747, (6, 1827): 1881.4580879108023, (6, 1828): 1881.5209508749379, (6, 1829): 1883.3922761369954, (6, 1830): 1885.9872453725511, (6, 1831): 1886.0458327040249, (6, 1832): 1884.7519766251455, (6, 1833): 1884.1783565869819, (6, 1836): 1882.4395143378654, (6, 1841): 1888.8699095215136, (6, 1843): 1886.5917301098136, (6, 1844): 1888.2762682743748, (6, 1845): 1886.1536729813029, (6, 1847): 1875.3920360091772, (6, 1848): 1878.6586913708295, (6, 1849): 1894.6370302802675, (6, 1850): 1895.6172880505521, (6, 1851): 1882.9564960714765, (6, 1852): 1884.7505067009272, (6, 1854): 1885.0807188135273, (6, 1856): 1876.9942573801816, (6, 1857): 1879.2876456826007, (6, 1858): 1892.0696973365218, (6, 1861): 1884.529931529735, (6, 1866): 1878.1374650918801, (6, 1867): 1887.7124231364714, (6, 1868): 1884.6091219534237, (6, 1870): 1890.0344161095607, (6, 1871): 1885.9878136877142, (6, 1875): 1883.863563912029, (6, 1880): 1877.6173289393755, (6, 1882): 1880.7957809962982, (6, 1883): 1893.9697135658937, (6, 1889): 1876.6740448752062, (6, 1893): 1881.0166321001304, (6, 1894): 1878.3894907308327, (6, 1899): 1873.6810700256506, (6, 1900): 1874.7569303212033, (6, 1902): 1884.8042528388255, (6, 1905): 1888.638518418366, (6, 1907): 1879.1921362809032, (6, 1910): 1878.3037446640626, (6, 1917): 1889.4875477059852, (6, 1920): 1878.0288605539602, (6, 1935): 1886.0306996846386, (6, 1937): 1888.9398050722227, (6, 1946): 1865.3095886294645, (6, 1949): 1867.14338347736, (6, 1950): 1861.859276774721, (6, 1951): 1865.2680995415442, (6, 1952): 1872.633613927547, (6, 1953): 1870.3416491407127, (6, 1954): 1870.9856633717789, (6, 1958): 1868.0833788622247, (6, 1960): 1873.5354128313204, (6, 1968): 1875.6774719122113, (6, 1969): 1883.5556844495625, (6, 1974): 1881.7653350017104, (6, 1975): 1882.7464837190653, (6, 1979): 1874.5657858202082, (6, 1980): 1877.122244695581, (6, 1981): 1877.0121787909916, (6, 1985): 1877.6523845206686, (6, 1994): 1865.3618363552657, (6, 2011): 1881.7268981022623, (6, 2019): 1907.742842908413, (6, 2020): 1904.3262375990425, (6, 2029): 1894.3274030247994, (6, 2030): 1901.9101459419037, (6, 2032): 1894.2329701748386, (6, 2033): 1898.0374693200317, (6, 2034): 1899.4459846395857, (6, 2036): 1895.1970902162004, (6, 2037): 1896.0397837209694, (6, 2038): 1889.8807404558138, (6, 2042): 1924.4632380258624, (6, 2050): 1894.293303823842, (6, 2051): 1895.4163799454718, (6, 2053): 1895.6216344950021, (6, 2054): 1898.7358221521629, (6, 2066): 1892.684179832963, (6, 2067): 1891.873438973711, (6, 2071): 1858.8111732170214, (6, 2072): 1863.2363935362375, (6, 2073): 1843.6379370717061, (6, 2074): 1843.9101985110944, (6, 2080): 1837.0501010509226, (6, 2082): 1865.9879929568933, (6, 2083): 1868.1799974875105, (6, 2089): 1860.9342817336649, (6, 2090): 1862.7036954581224, (6, 2092): 1858.1561942237977, (6, 2098): 1838.5651737482979, (6, 2099): 1842.7529815599478, (6, 2101): 1839.4087690130316, (6, 2102): 1852.6164527920732, (6, 2103): 1849.042698360082, (6, 2104): 1847.7652575076104, (6, 2106): 1870.7408280788034, (6, 2112): 1842.4979840207145, (6, 2113): 1855.3777066907915, (6, 2114): 1861.0395683293773, (6, 2117): 1873.9986353815432, (6, 2123): 1797.6779821039902, (6, 2124): 1800.4173429964908, (6, 2134): 1796.3676520466925, (6, 2138): 1802.9213276627743, (6, 2141): 1796.1604130060373, (6, 2148): 1814.7586483388739, (6, 2150): 1790.1976114304812, (6, 2151): 1794.1468846710789, (6, 2152): 1789.67890951798, (6, 2153): 1814.2871308981157, (6, 2154): 1802.0412598434948, (6, 2155): 1803.2160945152, (6, 2156): 1799.3356141179781, (6, 2157): 1811.2646739409122, (6, 2160): 1813.7620768410382, (6, 2161): 1790.6559913242709, (6, 2162): 1820.3159990811437, (6, 2163): 1815.9821145461403, (6, 2164): 1816.616534216606, (6, 2168): 1798.7966614445531, (6, 2172): 1808.0660669319027, (6, 2174): 1795.6517144844652, (6, 2178): 1812.2825536080322, (6, 2179): 1811.070080169763, (6, 2183): 1804.4172953260547, (6, 2185): 1805.4896914135265, (6, 2186): 1802.825853346288, (6, 2190): 1812.7062598807233, (6, 2192): 1808.2206864460318, (6, 2193): 1804.6823956018454, (6, 2194): 1800.1064407765584, (6, 2195): 1801.3756973078225, (6, 2197): 1810.1477015319806, (6, 2205): 1806.4813840282443, (6, 2207): 1801.1129775271568, (6, 2208): 1804.5003926447719, (6, 2212): 1801.794842178425, (6, 2214): 1744.7790891558432, (6, 2225): 1760.7254975003373, (6, 2231): 1698.6173624048688, (6, 2278): 1816.6940424772765, (6, 2284): 1828.8850546907208, (6, 2285): 1828.9230715892288, (6, 2291): 1819.720626556578, (6, 2292): 1811.2328770487875, (6, 2307): 1823.2877002013902, (6, 2313): 1820.8749076348147, (6, 2317): 1800.369440627026, (6, 2319): 1815.3598752857154, (6, 2321): 1821.2214635850255, (6, 2323): 1817.7464164166936, (6, 2326): 1828.1241595575061, (6, 2327): 1824.1932105903038, (6, 2329): 1821.8116894545724, (6, 2330): 1819.788114004752, (6, 2332): 1827.630506141521, (6, 2344): 1813.4128884213571, (6, 2346): 1815.2677214331557, (6, 2361): 1796.759070994431, (6, 2368): 1852.4405817757527, (6, 2374): 1858.3472637946272, (6, 2375): 1858.7940193134339, (6, 2377): 1842.079774978116, (6, 2378): 1862.407831084275, (6, 2379): 1864.8243498601255, (6, 2380): 1864.893801383879, (6, 2383): 1844.9179286163192, (6, 2385): 1846.5700123573085, (6, 2395): 1845.0331486823795, (6, 2397): 1863.9216864425323, (6, 2398): 1836.9810071648847, (6, 2399): 1841.5737242644086, (6, 2400): 1840.2904043941778, (6, 2402): 1854.7578918988995, (6, 2403): 1858.3447418612568, (6, 2404): 1858.4372577143465, (6, 2405): 1850.5415763124688, (6, 2407): 1855.768238190467, (6, 2408): 1860.839249447067, (6, 2409): 1852.61881612247, (6, 2411): 1861.695193625735, (6, 2412): 1859.4877936237783, (6, 2413): 1862.8927080723042, (6, 2414): 1858.570801612682, (6, 2422): 1861.7829213987834, (6, 2424): 1859.7588716922369, (6, 2426): 1859.8484281193562, (6, 2433): 1854.5168679830674, (6, 2436): 1854.9633569475438, (6, 2437): 1833.558773865751, (6, 2440): 1837.6703123569166, (6, 2445): 1947.6630718386125, (6, 2447): 1934.4799627140476, (6, 2454): 1945.0318687242086, (6, 2455): 1944.0116742098357, (6, 2460): 1913.4024062113801, (6, 2461): 1917.5303290121742, (6, 2471): 1991.6221596386738, (6, 2492): 1986.1379160074944, (6, 2511): 1943.5235476605635, (6, 2523): 1965.551101507744, (6, 2525): 1964.1991652290828, (6, 2535): 1938.8762343815142, (6, 2537): 1932.8588866193634, (6, 2538): 1935.3983275017788, (6, 2539): 1941.3156431449693, (6, 2540): 1941.8102408153154, (6, 2542): 1948.9499197245864, (6, 2559): 2030.2789434541362, (6, 2575): 2030.780508211592, (6, 2599): 1860.918567653239, (6, 2600): 1899.2276280549634, (6, 2607): 1870.984875776012, (6, 2627): 1991.4200801149436, (6, 2647): 2015.3002098701584, (6, 2674): 1997.1586861395476, (6, 2681): 1998.8017340637773, (6, 2683): 2005.902811922597, (6, 2686): 1993.5323480983777, (6, 2689): 2117.7053754782323, (6, 2690): 2119.2961862692728, (6, 2713): 2172.680961737317, (6, 2714): 2178.8044312473075, (6, 2715): 2181.561184552311, (6, 2739): 2177.9080238292954, (6, 2740): 2149.0774391619875, (6, 2741): 2149.642638839449, (6, 2749): 2178.411426015397, (6, 2750): 2177.8216226458535, (6, 2752): 2179.131023608935, (6, 2755): 2182.237445096509, (6, 2758): 2182.8218985002195, (6, 2759): 2182.1775574100384, (6, 2769): 2177.302231794848, (6, 2771): 2156.524505676248, (6, 2779): 2167.9955687782485, (6, 2784): 2141.2001868411285, (6, 2800): 2157.3106967356703, (6, 2802): 2149.3431160284113, (6, 2803): 2146.951406209277, (6, 2804): 2144.555921710256, (6, 2805): 2155.7109883407156, (6, 2807): 2154.1907245563766, (6, 2809): 2156.152016404869, (6, 2812): 2134.770790187687, (6, 2814): 2164.111334033048, (6, 2817): 2176.762278037106, (6, 2819): 2151.2635827426393, (6, 2823): 2148.159233133427, (6, 2832): 2161.0975068063412, (6, 2836): 2148.2774301092454, (6, 2839): 2152.785837936738, (6, 2841): 2171.2884711597735, (6, 2843): 2168.1887045354974, (6, 2846): 2156.234983799155, (6, 2849): 2165.365016431402, (6, 2852): 2161.5938942213206, (6, 2853): 2167.183569590715, (6, 2876): 2174.7371543790828, (6, 2877): 2185.941378821352, (6, 2885): 2201.776305973658, (6, 2918): 2144.1187092363057, (6, 2921): 2150.1697486249955, (6, 2925): 2117.4223948136823, (6, 2926): 2103.9922583420253, (6, 2930): 2141.219300868239, (6, 2931): 2123.056156683586, (6, 2938): 2146.513017697744, (6, 2940): 2148.474301320125, (6, 2947): 2130.271183254978, (6, 2949): 2135.792289052702, (6, 2950): 2140.1004653842233, (6, 2952): 2137.961623016915, (6, 2958): 2136.583368160562, (6, 2959): 2136.0459858726845, (6, 2960): 2141.855909527051, (6, 2961): 2140.548278557763, (6, 2963): 2136.0484356758766, (6, 2968): 2138.821812069421, (6, 2976): 2134.063115804203, (6, 2981): 2109.111430432045, (6, 2982): 2110.6918261882593, (6, 2984): 2109.195113252626, (6, 3003): 2108.512732411608, (6, 3046): 2048.976545400483, (6, 3050): 2085.92198365442, (6, 3051): 2086.5574266493, (6, 3053): 2083.0104393732277, (6, 3069): 2113.909272965558, (6, 3071): 2075.5540961509896, (6, 3080): 2206.4263603831964, (6, 3199): 2118.50644224735, (6, 3200): 2115.5140122692605, (6, 3205): 2143.9395252929903, (6, 3209): 2118.3686878744766, (6, 3215): 2114.2806487652897, (6, 3217): 2108.7199876207296, (6, 3249): 2113.1735821274924, (6, 3263): 2154.5976611159103, (6, 3289): 2122.122030144196, (6, 3301): 2127.442422083436, (6, 3302): 2123.9676571216155, (6, 3307): 2121.0433479073763, (6, 3310): 2129.846011946514, (6, 3391): 2211.327759890807, (6, 3509): 1182.3660270546593, (6, 3510): 1178.886730056598, (6, 3511): 1178.7411594521695, (6, 3512): 1174.431057097862, (6, 3514): 1173.2095155751717, (6, 3519): 1202.5540347670078, (6, 3536): 1184.1954663888255, (6, 3545): 1187.2131237957979, (6, 3548): 1178.6237924671698, (6, 3572): 1189.1656321493965, (6, 3581): 1193.1196848687555, (6, 3583): 1180.6330562625346, (6, 3601): 1212.9150602065497, (6, 3656): 1216.6067974928933, (6, 3669): 1230.0369698370694, (6, 3670): 1234.0040464378671, (6, 3695): 1207.8362327091988, (6, 3696): 1209.9171274989426, (6, 3782): 1137.1982723810145, (6, 3792): 1139.8491891669216, (6, 3989): 1505.4966809020548, (6, 4008): 1530.7456250611406, (6, 4031): 1537.5451790164482, (6, 4045): 1520.5419273419636, (6, 4144): 1513.9495870413102, (6, 4145): 1479.8548551659842, (6, 4164): 1502.1382141472543, (6, 4168): 1490.1780537404015, (6, 4173): 1486.528551635281, (6, 4181): 1471.1634135744525, (6, 4228): 1465.9144974355017, (6, 4248): 1447.0691175584332, (6, 4254): 1268.8476615524858, (6, 4260): 1273.83472126124, (6, 4262): 1279.8406080703364, (6, 4273): 1280.7650656330745, (6, 4319): 1172.0308873777315, (6, 4326): 1170.2754720155674, (6, 4328): 1172.7112768465138, (6, 4334): 1174.3610448218976, (6, 4335): 1171.4100576072342, (6, 4372): 663.3905599162844, (6, 4413): 717.0086765116023, (6, 4434): 663.7223916733695, (6, 4447): 680.5375403681797, (6, 4452): 663.1824983919158, (6, 4463): 481.9002468490031, (6, 4465): 489.72047797413416, (6, 4619): 701.5162506556983, (6, 4645): 721.9704094077432, (6, 4657): 716.4844347513475, (6, 4666): 707.3830666755097, (6, 4676): 719.3737371437139, (6, 4678): 723.3533783271083, (6, 4689): 711.9184182582205, (6, 4704): 771.1613299472202, (6, 4726): 868.4064340692466, (6, 4727): 866.2419503224454, (6, 4730): 862.1939950610778, (6, 4731): 862.4498273650908, (6, 4734): 870.0490538815326, (6, 4735): 867.2198570295202, (6, 4736): 867.5462559980791, (6, 4737): 863.0018694427101, (6, 4738): 862.9234580705333, (6, 4756): 864.6501958437142, (6, 4760): 857.945929188693, (6, 4761): 860.7962286155478, (6, 4762): 854.0617493508918, (6, 4765): 858.4927803566171, (6, 4773): 873.4232937358017, (6, 4774): 870.1851048772787, (6, 4790): 872.1777607020618, (6, 4795): 870.6165464457688, (6, 4799): 870.4435433715779, (6, 4801): 873.2972269770137, (6, 4804): 873.0117823217576, (6, 4805): 871.7234891570102, (6, 4806): 867.4608621082041, (6, 4815): 864.2447300189282, (6, 4816): 870.308886535016, (6, 4817): 869.9603096065914, (6, 4826): 867.1189031700183, (6, 4830): 863.3822127601276, (6, 4839): 864.0246498434872, (6, 4840): 865.2367875434304, (6, 4841): 860.202355487212, (6, 4846): 859.0035665803965, (6, 4848): 857.1393033743036, (6, 4850): 858.8390824748878, (6, 4871): 841.2413314000933, (6, 4883): 857.6497397107087, (6, 4900): 851.2359765704532, (6, 4901): 847.4827440356202, (6, 4917): 665.123185418913, (6, 4931): 648.9709305822385, (6, 4944): 668.2213551915964, (6, 4956): 650.6361815354455, (6, 4958): 647.6574308599635, (6, 4959): 642.8719416779632, (6, 4961): 654.9358343461186, (6, 4966): 645.2281569872396, (6, 5207): 627.20228302551, (6, 5272): 560.88252287247, (6, 5283): 560.3784739480342, (6, 5287): 547.4030277427591, (6, 5289): 546.8699930527017, (6, 5293): 573.1937102937264, (6, 5295): 573.715359471063, (6, 5296): 566.1033880253686, (6, 5298): 561.8580464899171, (6, 5303): 555.774738126576, (6, 5305): 545.8515079009891, (6, 5306): 534.8562412915536, (6, 5307): 545.1764878507666, (6, 5308): 543.3789104861632, (6, 5313): 553.1006699822383, (6, 5314): 556.069253279536, (6, 5317): 538.3596707719284, (6, 5319): 553.494333765713, (6, 5324): 559.0877918535077, (6, 5326): 563.1800532812846, (6, 5348): 528.1874043664648, (6, 5351): 517.4862311800532, (6, 5399): 536.2130210433442, (6, 5413): 501.0630469738269, (6, 5422): 543.9913395068289, (6, 5445): 539.3441755989094, (6, 5448): 538.8262734052017, (6, 5456): 530.6357200668573, (6, 5467): 529.0035221029156, (6, 5624): 555.6432434067162, (6, 5671): 676.9457137543956, (6, 5672): 675.7155366276199, (6, 5797): 708.0480808254113, (6, 5871): 494.9626964165461, (6, 5976): 466.81446813539526, (6, 6118): 1806.4425275813894, (6, 6248): 1946.8749933348522, (6, 6345): 972.8642452384082, (6, 6352): 977.9010099987887, (6, 6354): 969.1945766820857, (6, 6359): 972.7359770980308, (6, 6376): 988.0303654189084, (6, 6378): 970.2655039025929, (6, 6381): 976.2205054624073, (6, 6383): 972.1047435348523, (6, 6396): 994.4414293859301, (6, 6399): 978.196996312718, (6, 6408): 973.2188270749392, (6, 6409): 958.9657291299515, (6, 6419): 948.8222434066273, (6, 6422): 963.1996506130685, (6, 6423): 962.9513776456231, (6, 6424): 956.3636954247626, (6, 6439): 953.4369449150375, (6, 6464): 951.041023047586, (6, 6465): 955.5929675118525, (6, 6469): 963.5967335820471, (6, 6470): 965.8785915497439, (6, 6472): 972.943439839697, (6, 6480): 954.2438707824818, (6, 6486): 930.9419947021412, (6, 6497): 937.7255488810491, (6, 6503): 926.8376306482946, (6, 6508): 939.4459639765331, (6, 6509): 932.6924933624329, (6, 6521): 944.8841703576421, (6, 6544): 932.8318186363896, (6, 6552): 941.2010227807932, (6, 6553): 940.647445835494, (6, 6554): 940.261067216775, (6, 6578): 943.9541005648243, (6, 6582): 930.8623170855983, (6, 6601): 941.4508675725039, (6, 6609): 956.973632564555, (6, 6610): 954.3285484049983, (6, 6611): 961.3859874929619, (6, 6614): 965.4608215903094, (6, 6615): 963.0565619991016, (6, 6616): 954.1646617756229, (6, 6617): 957.277846078934, (6, 6618): 948.3560560889355, (6, 6619): 963.9148741620933, (6, 6620): 949.8056332237129, (6, 6621): 948.7446361530027, (6, 6622): 951.8078977733782, (6, 6623): 960.6953388121234, (6, 6624): 955.9970910055266, (6, 6625): 958.3208937917279, (6, 6626): 965.8075932856317, (6, 6627): 969.2242200006458, (6, 6628): 945.319372098548, (6, 6629): 950.6785515414832, (6, 6630): 965.1836127354798, (6, 6632): 953.0880258805325, (6, 6634): 962.2535426969771, (6, 6635): 951.0471510892271, (6, 6636): 952.663245786794, (6, 6637): 949.9924392360351, (6, 6638): 961.0550072287608, (6, 6639): 966.7024133477172, (6, 6640): 963.2808648959925, (6, 6641): 945.3176471597366, (6, 6642): 958.1555265715633, (6, 6643): 968.8893007155707, (6, 6645): 961.955962587119, (6, 6646): 951.7291766610156, (6, 6647): 959.8095053284701, (6, 6653): 964.3901017524335, (6, 6655): 968.1165507353628, (6, 6658): 960.5408661997297, (6, 6662): 955.0277630372279, (6, 6819): 900.792555077393, (6, 6996): 830.3682973598533, (6, 7059): 832.5570418196354, (6, 7187): 681.1356169483307, (6, 7304): 772.6315241961871, (6, 7528): 766.1399686745459, (6, 7720): 853.6592474610208, (6, 7793): 829.1923572111225, (6, 7807): 837.6207219897631, (6, 7808): 823.5182829801772, (6, 7831): 928.6023634865177, (6, 7850): 955.4700430709216, (6, 7852): 960.1846266858894, (6, 8012): 883.3867556440109, (6, 8125): 734.4054503811034, (6, 8208): 871.5146138248006, (6, 8392): 864.801248514375, (6, 8651): 921.7660857694739, (6, 9088): 987.0274111598644, (6, 9443): 729.9908362217524, (6, 9444): 724.6808212744398, (6, 9828): 725.2496200308577, (6, 9868): 806.86208384624, (6, 10180): 725.3452908625601, (6, 10256): 755.1192719132558, (6, 10276): 757.8432049065274, (6, 10378): 821.3392269925728, (6, 10676): 623.5415866435874, (6, 10714): 580.1397683604786, (6, 10730): 653.0626128118969, (6, 10862): 77.85460342874714, (6, 10881): 93.36632975044962, (6, 10883): 91.47337178326337, (6, 10885): 74.58446748129201, (6, 10891): 88.66962286251471, (6, 10909): 87.59586472815587, (6, 10911): 90.42804839324923, (6, 10913): 86.60879625924585, (6, 10915): 86.88251726730215, (6, 10919): 89.45577499209915, (6, 11037): 57.42100302844822, (6, 11039): 63.34062827660197, (6, 11516): 1849.244382525261, (6, 11856): 1176.1518373609097, (6, 11857): 1166.1711345988178, (6, 11861): 1171.1110466908412, (6, 11881): 1177.0284223432052, (6, 11902): 1164.0812631622532, (6, 11911): 1168.801218468448, (6, 11914): 1167.5088499611413, (6, 11922): 1174.6642168575631, (6, 11924): 1179.5236597917578, (6, 11926): 1176.2054736705156, (6, 11950): 1191.2683412298593, (6, 11963): 1202.4144851054489, (6, 11983): 1206.712110850034, (6, 11985): 1207.4149032032929, (6, 12009): 1215.6055514249038, (6, 12010): 1205.0553814705206, (6, 12018): 1207.79081276379, (6, 12020): 1208.446872873828, (6, 12021): 1210.930254730459, (6, 12024): 1218.6348669948381, (6, 12025): 1213.887546638824, (6, 12027): 1212.5905216844233, (6, 12031): 1203.6547983849384, (6, 12032): 1204.6571544643311, (6, 12035): 1217.5088515475002, (6, 12041): 1202.2586193940635, (6, 12045): 1109.1966695936862, (6, 12145): 1167.3673609163088, (6, 12275): 1533.9354409688704, (6, 12294): 1523.5725773952554, (6, 12358): 1602.2226399926965, (6, 12463): 1640.326585658689, (6, 12465): 1640.196568906684, (6, 12482): 1641.9334353340294, (6, 12503): 1642.7953614467874, (6, 12506): 1645.7166559058478, (6, 12549): 1627.6280287445704, (6, 12559): 1627.7560102370596, (6, 12569): 1634.32133237335, (6, 12572): 1636.273980083108, (6, 12574): 1630.896113686748, (6, 12576): 1628.7398179149545, (6, 12591): 1621.4393318535865, (6, 12608): 1634.0487691273677, (6, 12696): 1601.4694905960355, (6, 12710): 1608.8579895823375, (6, 12728): 1610.5049871789793, (6, 12766): 1167.871795201239, (6, 12771): 1119.6656719311093, (6, 12790): 1118.3737328357324, (6, 12795): 1119.28571991131, (6, 12797): 1076.9014298915279, (6, 12798): 1078.9268681050382, (6, 12811): 1099.9475363248182, (6, 12830): 1098.6710125242616, (6, 12848): 1090.5480729543838, (6, 12850): 1085.2384223301594, (6, 12852): 1094.1546094447374, (6, 12854): 1091.0454119316669, (6, 12859): 1090.5923464218013, (6, 12861): 1079.686415081635, (6, 12865): 1108.9860523934328, (6, 12866): 1103.9085439112848, (6, 12867): 1113.3522409379345, (6, 12874): 1109.2492228561464, (6, 12875): 1110.1703381020698, (6, 12881): 1104.3551617110843, (6, 12883): 1107.8305977565183, (6, 12885): 1113.0408021504422, (6, 12888): 1103.7528881180665, (6, 12889): 1100.6189298548682, (6, 12892): 1111.2531592763273, (6, 12893): 1106.2702710865726, (6, 12896): 1105.7260755807547, (6, 12906): 1119.9868191654675, (6, 13018): 1156.1904739107147, (6, 13071): 1170.5123620205316, (6, 13131): 1092.9735308351578, (6, 13146): 1098.826959942214, (6, 13159): 1148.6526144465888, (6, 13193): 1085.4604483228252, (6, 13198): 1032.5818686411046, (6, 13292): 1058.9977892063507, (6, 13296): 1043.6850548437933, (6, 13406): 1057.4747904229635, (6, 13407): 1059.9806664100818, (6, 13417): 1084.4001548247502, (6, 13418): 1091.2217710817604, (6, 13438): 1081.391811889179, (6, 13442): 1074.8919563788354, (6, 13443): 1073.9098919617888, (6, 13764): 1188.5873320619028, (6, 13766): 1188.0156288601543, (6, 13771): 1198.7923997539885, (6, 13783): 1171.979368877082, (6, 13784): 1183.0065584239685, (6, 13792): 1215.3112496306092, (6, 13824): 1174.4538373139828, (6, 14017): 1111.448278988788, (6, 14870): 148.76353192539983, (6, 14997): 669.3409007013122, (6, 15000): 663.6183742901892, (6, 15003): 657.8859690194773, (6, 15006): 683.1924590692641, (6, 15007): 682.6477329167077, (6, 15056): 665.4814624513912, (6, 15063): 662.0585557899507, (6, 15069): 655.5306117459146, (6, 15076): 678.5980712112954, (6, 15086): 685.8703547530095, (6, 15087): 677.8605919545589, (6, 15111): 683.8637346001874, (6, 15116): 679.7975102409057, (6, 15722): 695.4722905864924, (6, 15998): 565.8345077852478, (6, 16073): 1666.9472867737568, (6, 16939): 1684.2885205607206, (6, 16940): 1677.8819250048819, (6, 16951): 1690.9993543220103, (6, 16963): 1690.1753368659226, (6, 16965): 1695.4102919629154, (6, 16969): 1697.1762366842795, (6, 16970): 1690.9378541256203, (6, 16971): 1686.0112578627422, (6, 16973): 1687.7815691447363, (6, 16974): 1699.5250800109102, (6, 16976): 1689.9927456778225, (6, 16978): 1685.655970826842, (6, 16980): 1690.0329103576498, (6, 16982): 1701.6733931151896, (6, 17045): 2034.6263497209914, (6, 17048): 2042.3691084450231, (6, 17304): 1400.0855953556816, (6, 17305): 1402.6339449441944, (6, 17330): 1404.1809096051384, (6, 17334): 1391.7997497629942, (6, 17343): 1410.8058012773379, (6, 17345): 1398.0740940972576, (6, 17347): 1407.9289062773016, (6, 17351): 1382.0777808085677, (6, 17372): 1393.476052445183, (6, 17373): 1409.3915013077037, (6, 17377): 1411.0418896494964, (6, 17382): 1402.0560549568743, (6, 17383): 1401.5412102291405, (6, 17389): 1396.7683982599779, (6, 17400): 1404.8452449634194, (6, 17401): 1403.6325853218705, (6, 17402): 1406.0050618625628, (6, 17403): 1407.429097114028, (6, 17440): 1405.6822882567133, (6, 17455): 1413.5207903824955, (6, 17491): 1419.1705695304147, (6, 17507): 1371.2522843951574, (6, 17509): 1374.3354750300134, (6, 17590): 1386.2182311042948, (6, 17615): 1317.5257775744262, (6, 17642): 1325.6158768877697, (6, 17643): 1327.760583420142, (6, 17668): 1315.7258318427014, (6, 17721): 1290.0663896737117, (6, 17754): 1330.6508234317375, (6, 17769): 1365.3258153443608, (6, 17776): 1358.5677525470594, (6, 17804): 1371.836258063826, (6, 17809): 1376.5607482215028, (6, 17824): 1369.3223904587242, (6, 17837): 1375.1160142393887, (6, 17838): 1379.3270409516902, (6, 17862): 1377.6103634835476, (6, 17866): 1385.8302467779658, (6, 17872): 1372.0050284126708, (6, 17873): 1366.5876836002, (6, 17881): 1375.4593187933863, (6, 17947): 1125.0772148759672, (6, 17951): 1119.2402530061208, (6, 17953): 1115.796309722733, (6, 17954): 1114.6747423894947, (6, 17959): 1127.8718743126205, (6, 17963): 1129.875100020779, (6, 18000): 1094.4450425382265, (6, 18001): 1092.392833282755, (6, 18111): 1095.8947097727207, (6, 18148): 889.0892311331394, (6, 18166): 952.0734707551745, (6, 18189): 1042.0109482586279, (6, 18239): 1409.3287055958983, (6, 18240): 1409.9778447906333, (6, 18245): 1410.1357844080571, (6, 18247): 1409.8524595765653, (6, 18251): 1410.9763492452655, (6, 18256): 1413.0159799799455, (6, 18258): 1412.236273187422, (6, 18259): 1412.8295999005816, (6, 18260): 1413.821047806699, (6, 18262): 1415.1869274216544, (6, 18263): 1413.7286520159544, (6, 18264): 1414.6697542560646, (6, 18266): 1416.1656210175454, (6, 18267): 1416.986837271432, (6, 18268): 1417.6534317607525, (6, 18269): 1419.3646455341664, (6, 18275): 1418.5605287686865, (6, 18285): 1414.0718468454927, (6, 18308): 1396.083676187108, (6, 18313): 1391.9764874568416, (6, 18314): 1396.0604534490144, (6, 18315): 1417.3317830451622, (6, 18316): 1418.1556740937847, (6, 18317): 1419.0154987847577, (6, 18320): 1418.46079379342, (6, 18321): 1419.3586698969098, (6, 18322): 1420.5218794624213, (6, 18324): 1420.1266706195336, (6, 18325): 1422.4373953232664, (6, 18326): 1421.5331200613448, (6, 18327): 1420.5899319884406, (6, 18329): 1422.4245840169515, (6, 18330): 1424.1955106337343, (6, 18331): 1422.1870367954525, (6, 18332): 1420.6040550984312, (6, 18333): 1423.1183650729304, (6, 18336): 1420.4143308626287, (6, 18337): 1420.5984664225039, (6, 18403): 1424.7137813721465, (6, 18432): 1420.5766472860914, (6, 18451): 1423.5414703112883, (6, 18466): 1423.7673072028392, (6, 18481): 1415.4321297849945, (6, 18483): 1416.0998279187802, (6, 18484): 1414.3152940756884, (6, 18485): 1408.2582009169391, (6, 18486): 1409.2679292908747, (6, 18487): 1405.4874593639324, (6, 18489): 1411.1978448922375, (6, 18490): 1412.3241377958666, (6, 18491): 1413.716817737214, (6, 18492): 1403.0795248959423, (6, 18493): 1407.9658991660042, (6, 18494): 1411.1775400635129, (6, 18495): 1411.1852259641664, (6, 18496): 1410.2799214714466, (6, 18497): 1403.9896062753764, (6, 18498): 1407.425895617501, (6, 18499): 1409.848415849197, (6, 18501): 1406.8993353461192, (6, 18502): 1405.2709499226005, (6, 18503): 1404.8470567387708, (6, 18504): 1411.688999743525, (6, 18506): 1405.181682688642, (6, 18507): 1403.2413143524325, (6, 18508): 1408.8547711485373, (6, 18509): 1408.243498493666, (6, 18510): 1403.9387432750555, (6, 18511): 1407.0490070085614, (6, 18512): 1406.512542304461, (6, 18515): 1410.875410226862, (6, 18516): 1408.7703589814853, (6, 18517): 1405.740591354625, (6, 18518): 1410.6388679389229, (6, 18519): 1412.411484517651, (6, 18520): 1409.2073276375575, (6, 18522): 1420.2172869214614, (6, 18523): 1419.7993270909217, (6, 18532): 1420.8078528127865, (6, 18535): 1417.9569128169846, (6, 18537): 1416.3706527285121, (6, 18539): 1416.3170644883726, (6, 18540): 1416.0942402319295, (6, 18541): 1416.5382800056104, (6, 18542): 1416.8906065205008, (6, 18543): 1414.8394138709634, (6, 18546): 1414.5587336539022, (6, 18555): 1416.9778713574594, (6, 18556): 1416.9144125003568, (6, 18565): 1419.6291353355175, (6, 18567): 1418.8859532532092, (6, 18568): 1418.1858411918458, (6, 18577): 1427.9976678201003, (6, 18583): 1428.3811501029552, (6, 18605): 1432.8852266748158, (6, 18608): 1416.7611344580769, (6, 18616): 1441.9288873561152, (6, 18618): 1448.3576429259524, (6, 18625): 1451.0961283345982, (6, 18645): 1446.4354101219024, (6, 18646): 1446.4551977754716, (6, 18653): 1434.8239204855447, (6, 18654): 1440.8493501686567, (6, 18655): 1435.7780948913487, (6, 18666): 1470.1340034853063, (6, 18837): 1519.4934536748951, (6, 18974): 1440.3524346010172, (6, 18999): 1455.903801424889, (6, 19000): 1458.459504993767, (6, 19174): 1390.8232043804203, (6, 19342): 1455.8145298043628, (6, 19455): 1371.5593668167585, (6, 19555): 1283.3849459027335, (6, 19564): 1314.6456691484411, (6, 19573): 1304.531730140798, (6, 19586): 1298.418907462733, (6, 19605): 1296.3087942522588, (6, 19611): 1302.2142498309474, (6, 19614): 1292.832136622287, (6, 19641): 1362.3646218543897, (6, 19702): 1368.6550398215334, (6, 19713): 1361.9770599826809, (6, 19731): 1228.223064549785, (6, 19819): 1368.0391798487883, (6, 19893): 877.8070687053802, (6, 19899): 882.8870291303303, (6, 19929): 884.6789079167305, (6, 19951): 916.5423075701183, (6, 19962): 876.2866236588378, (6, 19970): 904.9259025768398, (6, 19971): 900.0043394704899, (6, 19972): 893.6959144069161, (6, 19975): 896.0350983637412, (6, 19978): 945.9014844756979, (6, 19987): 949.7930490930901, (6, 19989): 940.2228541680067, (6, 20039): 953.1879524995046, (6, 20043): 961.8389108654968, (6, 20047): 962.7104352411158, (6, 20052): 948.3971099233557, (6, 20054): 947.0385873807901, (6, 20085): 1028.1600842384453, (6, 20104): 1032.5509881102823, (6, 20132): 1001.5008029857072, (6, 20203): 829.1148058990522, (6, 20280): 810.3350004821427, (6, 20285): 803.0940525924202, (6, 20290): 814.9269986485303, (6, 20297): 812.8121612892777, (6, 20309): 914.5116976960319, (6, 20453): 1006.1666120521368, (6, 20485): 799.2489467686646, (6, 20520): 795.7494125088627, (6, 20526): 776.7300461018809, (6, 20698): 1382.572689329653, (6, 20868): 1464.1531804650062, (6, 21042): 945.9582666044524, (6, 21057): 978.3209293436755, (6, 21066): 954.8496580200566, (6, 21075): 959.599425632062, (6, 21093): 937.8657425225471, (6, 21098): 945.6265574186131, (6, 21127): 942.9936036687053, (6, 21130): 943.8839534762046, (6, 21144): 952.8452874317037, (6, 21146): 940.9756925953523, (6, 21147): 955.2729404239245, (6, 21148): 957.3168792046, (6, 21153): 982.9635636511406, (6, 21293): 986.2163844010176, (6, 21426): 1071.0756136931248, (6, 21442): 1121.9223347305074, (6, 21451): 1126.4297802380943, (6, 21466): 1091.4315862697724, (6, 21469): 1094.4858019215724, (6, 21471): 1090.0938163949202, (6, 21473): 1091.4883300549873, (6, 21475): 1089.0047862643414, (6, 21482): 1100.1274888247142, (6, 21484): 1097.5373594421526, (6, 21488): 1096.745836868005, (6, 21494): 1083.8228080373058, (6, 21498): 1087.4119425507654, (6, 21500): 1077.6574706017652, (6, 21514): 1067.0545680213925, (6, 21537): 1065.2487144205068, (6, 21662): 1057.452426338565, (6, 21691): 1040.6389325597695, (6, 21757): 1051.3437260375347, (6, 21777): 854.7025682301171, (6, 21778): 851.0754492422486, (6, 21779): 847.9523624423707, (6, 21790): 864.3782706844725, (6, 21802): 854.1524700598617, (6, 21824): 852.9435130633325, (6, 21874): 842.5867488939078, (6, 21879): 830.9852638788648, (6, 21983): 898.2963365212446, (6, 22002): 906.8123696579535, (6, 22132): 995.9433737761582, (6, 22261): 607.316223565661, (6, 22298): 588.3165154074267, (6, 22339): 603.5753453095116, (6, 22508): 553.8709322205303, (6, 22841): 2352.6788203240735, (6, 22842): 2351.3330339812, (6, 22874): 2331.7025051841174, (6, 22941): 2337.922513399858, (6, 22956): 2345.8371838119288, (6, 22960): 2351.825633047928, (6, 22968): 2341.917438577699, (6, 22970): 2347.148343040902, (6, 22974): 2339.677336923916, (6, 22980): 2350.4897693016314, (6, 23025): 2332.069976108981, (6, 23028): 2326.0565192329277, (6, 23081): 2322.599742696442, (6, 23104): 2272.948256753878, (6, 23147): 2227.765359970911, (6, 23298): 1119.9487463950934, (6, 23376): 1104.4244830883406, (6, 23381): 1073.6902284887901, (6, 23529): 1112.5597391286801, (6, 23556): 1106.1900879972493, (6, 23718): 1128.203049473431, (6, 24001): 1218.5754171394735, (6, 24094): 1214.6833499168506, (6, 24129): 1231.1554185888763, (6, 24174): 1183.5240596868707, (6, 24235): 1211.279595423169, (6, 24259): 1235.8816569821724, (6, 24260): 1233.3627777259935, (6, 24261): 1231.0580578679978, (6, 24305): 1258.5092837388024, (6, 24306): 1259.9791108028, (6, 24307): 1256.1398727287124, (6, 24308): 1281.3849268803513, (6, 24498): 1326.5033575666762, (6, 24499): 1326.2548029849138, (6, 24500): 1323.8321414048055, (6, 24668): 1335.9543930383754, (6, 24711): 1333.4420843514513, (6, 24756): 1333.5736465354619, (6, 24788): 1343.0120879227507, (6, 24809): 1313.3606735450826, (6, 24813): 1323.54112988291, (6, 24821): 1320.6178996207632, (6, 24825): 1320.9680792869365, (6, 24832): 1312.8038178762104, (6, 24833): 1316.2824589641114, (6, 24835): 1319.1987384773101, (6, 24837): 1326.0243662795604, (6, 24840): 1311.6018725068554, (6, 24841): 1318.3498081119583, (6, 24844): 1310.8619463209975, (6, 24845): 1317.5377116301675, (6, 24846): 1312.3020896281143, (6, 24849): 1313.769378579997, (6, 24850): 1323.5103864080668, (6, 24863): 1281.7599520834412, (6, 24866): 1288.2817556474276, (6, 24885): 1292.608535128376, (6, 24886): 1291.1867069756734, (6, 24889): 1311.8230645595213, (6, 24903): 1320.1629915403314, (6, 24909): 1302.2579844185234, (6, 24999): 1594.0731775684314, (6, 25019): 1593.5515572467016, (6, 25028): 1588.8349823542906, (6, 25137): 759.3816754880169, (6, 25145): 766.2889585325726, (6, 25208): 799.5257386736718, (6, 25233): 788.4009693912742, (6, 25371): 794.0673891098153, (6, 25377): 786.1724387522696, (6, 25828): 550.616277487616, (6, 25851): 560.2612760605826, (6, 25874): 570.3928755901978, (6, 25898): 551.4764806383217, (6, 25946): 550.0152539247899, (6, 26047): 556.9984577832248, (6, 26066): 768.5571180764525, (6, 26197): 652.2644256492728, (6, 26212): 394.3563481785998, (6, 26253): 382.3415434985287, (6, 26254): 389.3139225820953, (6, 26257): 385.52539746656225, (6, 26258): 382.35513985729085, (6, 26260): 384.5493463226268, (6, 26266): 398.4017889733182, (6, 26267): 398.1017912836833, (6, 26271): 395.9258947476247, (6, 26304): 450.473942709637, (6, 26305): 455.7909629237074, (6, 26363): 506.52229922339365, (6, 26441): 445.0837200885873, (6, 26442): 446.4024109541101, (6, 26450): 439.2072608688619, (6, 26459): 427.29538827676623, (6, 26462): 423.2907125842364, (6, 26467): 443.29675969709507, (6, 26471): 443.15035942159597, (6, 26472): 444.19710987662233, (6, 26473): 445.55887530074943, (6, 26476): 458.935159484755, (6, 26485): 436.18812159076816, (6, 26493): 442.2260394185059, (6, 26524): 421.1867817502971, (6, 26525): 423.4912123829717, (6, 26556): 439.89175493430594, (6, 26560): 429.9428015162425, (6, 26561): 423.4472194146026, (6, 26564): 440.59842162260765, (6, 26569): 425.47634037383654, (6, 26570): 427.35108868197415, (6, 26573): 433.4412645354323, (6, 26581): 437.75789725075015, (6, 26583): 433.5319036718917, (6, 26593): 443.47965061144555, (6, 26837): 449.14500176582817, (6, 26844): 451.8798634315402, (6, 26863): 456.86724541186925, (6, 26893): 468.8291560060916, (6, 26902): 473.02570448554746, (6, 26905): 459.28199496150256, (6, 26912): 465.59800982034056, (6, 26921): 461.85284618871196, (6, 26922): 469.9699847027051, (6, 27212): 299.36674338033885, (6, 27218): 286.28535846436125, (6, 27239): 312.6086071125841, (6, 27257): 308.2754682716271, (6, 27274): 316.15249154911834, (6, 27279): 316.9347195987683, (6, 27282): 309.7450280036226, (6, 27283): 308.43188134854483, (6, 27285): 320.7006284446948, (6, 27286): 317.8495957897244, (6, 27290): 304.01072037720644, (6, 27295): 296.31656292349913, (6, 27300): 316.58396408577505, (6, 27344): 307.51253367706306, (6, 27366): 317.6768997597959, (6, 27383): 325.80654429382815, (6, 27398): 329.5420784003833, (6, 27406): 320.7589670496975, (6, 27407): 321.30340475665724, (6, 27426): 298.5848614779894, (6, 27432): 270.4720191954896, (6, 27460): 286.1325163030388, (6, 27523): 359.75861513662534, (6, 27545): 447.72623772244475, (6, 27602): 637.9158725615092, (6, 27606): 639.5333517519739, (6, 27646): 489.49972073826734, (6, 27667): 524.3260064021417, (6, 27672): 524.5447746963388, (6, 27674): 519.5686756760846, (6, 27688): 518.2662702465226, (6, 27692): 532.4789730025293, (6, 27693): 527.5578226808258, (6, 27705): 529.1438287849951, (6, 27712): 533.1322650037298, (6, 27786): 611.7766883696466, (6, 27790): 583.0300280745115, (6, 27791): 580.3671471840702, (6, 27795): 601.8902659817247, (6, 27801): 580.7152492452411, (6, 27813): 618.6124198269257, (6, 27816): 609.9863738986135, (6, 27823): 579.867837846327, (6, 27830): 599.7399077587751, (6, 27884): 455.13977495200754, (6, 27885): 478.1563910010035, (6, 27896): 462.54512208023203, (6, 27919): 459.46907818541195, (6, 27922): 465.3854101866391, (6, 27930): 455.58731382764256, (6, 27934): 458.3249755726176, (6, 27935): 461.1213253256893, (6, 27948): 690.7015530505437, (6, 27951): 674.0412100060927, (6, 28061): 826.6941169623618, (6, 28290): 1060.8207663047583, (6, 28292): 1075.624369093364, (6, 28293): 1064.375013483446, (6, 28295): 1067.088941885005, (6, 28296): 1063.3611678723041, (6, 28297): 1053.553122658252, (6, 28302): 1056.1290383172473, (6, 28310): 1605.9137204063748, (6, 28313): 1622.283956317884, (6, 28372): 1601.5142736929427, (6, 28398): 1603.6664490738774, (6, 28399): 1602.9128848782946, (6, 28400): 1606.9723202563284, (6, 28401): 1593.5860887201034, (6, 28445): 1625.6235855636112, (6, 28475): 1570.1266930554202, (6, 28885): 1156.8876193244976, (6, 28886): 1151.5606390245741, (6, 28915): 1144.8956929918347, (6, 28916): 1145.3036341985303, (6, 28917): 1141.6543450425545, (6, 28921): 1164.5315279495185, (6, 28931): 1161.2536688668577, (6, 28945): 1114.9629739571594, (6, 28982): 1129.0098922904137, (6, 29219): 1096.319747782978, (6, 29228): 1085.1984794639657, (6, 29246): 1135.6591255509377, (6, 29248): 1125.6606338502327, (6, 29282): 1112.6610318832027, (6, 29290): 1152.2702277209419, (6, 29291): 1146.7716549090298, (6, 29292): 1150.6426972545673, (6, 29293): 1145.0902284994984, (6, 29294): 1145.7275489320718, (6, 29298): 1143.1505169259406, (6, 29299): 1140.28074181529, (6, 29304): 1140.4109925072382, (6, 29317): 1130.4543582321967, (6, 29323): 1129.9652582307756, (6, 29330): 1134.3032250377146, (6, 29331): 1138.4961148701034, (6, 29344): 1078.791556547985, (6, 29445): 913.5766447026742, (6, 29724): 2379.6143436724215, (6, 29738): 2382.394784509247, (6, 29745): 2376.21926894591, (6, 29748): 2387.61644684488, (6, 29750): 2396.2809750603205, (6, 29759): 2382.601654594346, (6, 29772): 2393.0445989882387, (6, 29781): 2391.0450947426384, (6, 29784): 2385.057702247946, (6, 29790): 2395.041145547991, (6, 29811): 2393.428914353406, (6, 29817): 2438.090847078924, (6, 29818): 2436.302861590869, (6, 29929): 2369.1250469788356, (6, 30039): 2378.0193004053785, (6, 30066): 2338.6228030624784, (6, 30116): 2265.540188046696, (6, 30238): 2156.471195643729, (6, 30248): 2181.5909857507095, (6, 30260): 2180.305438736655, (6, 30545): 1146.1109084664145, (6, 30733): 1048.2917147894457, (6, 30756): 964.1921085195936, (6, 30921): 1039.465485433417, (6, 31079): 1105.789163420032, (6, 31149): 1045.6509608737495, (6, 31154): 1053.9967350802679, (6, 31160): 1043.8559109671965, (6, 31163): 1052.4506308946725, (6, 31189): 996.0561608785979, (6, 31215): 1006.9322583267016, (6, 31259): 1039.0743733692752, (6, 31262): 1031.2710906977827, (6, 31430): 1134.1416974909964, (6, 31568): 1087.3882186909634, (6, 31751): 1100.1952484677788, (8, 109): 1226.8275966352403, (8, 872): 2701.399007813974, (8, 873): 2709.385002741178, (8, 877): 2706.1218743857085, (8, 879): 2707.2803545773236, (8, 884): 2698.65515255823, (8, 889): 2703.7876962198507, (8, 891): 2696.085820354302, (8, 892): 2713.526033143349, (8, 894): 2712.6276781185693, (8, 896): 2705.375029468173, (8, 903): 2706.114657657067, (8, 909): 2693.3921218470255, (8, 910): 2696.835638531289, (8, 912): 2691.494055687471, (8, 913): 2685.518629802855, (8, 916): 2683.345541057992, (8, 926): 2699.7765141973728, (8, 927): 2697.147586383926, (8, 948): 2693.2351310839676, (8, 961): 2698.9187372106444, (8, 962): 2699.996711232302, (8, 963): 2701.1527763536833, (8, 967): 2709.6000951601104, (8, 974): 2704.683515475087, (8, 998): 2712.5373700570676, (8, 1014): 2890.328138318318, (8, 1086): 2688.1750637429845, (8, 1087): 2687.8354652462685, (8, 1089): 2680.067623195331, (8, 1090): 2683.401963168962, (8, 1092): 2694.9889220089294, (8, 1097): 2686.0178144941865, (8, 1107): 2701.1821041472326, (8, 1387): 1475.0338122525104, (8, 1554): 1347.3907387321678, (8, 1827): 3058.351680512995, (8, 1828): 3059.3727652278753, (8, 1829): 3060.4732405265886, (8, 1830): 3058.379851690687, (8, 1831): 3059.2423240952658, (8, 1832): 3058.4669131653836, (8, 1833): 3058.706190932461, (8, 1836): 3057.9500312349096, (8, 1841): 3062.836764069494, (8, 1843): 3060.7013860347097, (8, 1844): 3061.5098483934107, (8, 1845): 3058.8423574995054, (8, 1847): 3051.031806453649, (8, 1848): 3053.8145652716075, (8, 1849): 3066.7123443512683, (8, 1850): 3068.210580360822, (8, 1851): 3055.563595714167, (8, 1852): 3055.437300267439, (8, 1854): 3057.03163378243, (8, 1856): 3050.200370786953, (8, 1857): 3053.444756009467, (8, 1858): 3065.674199636138, (8, 1861): 3060.014082625747, (8, 1866): 3049.7368928953388, (8, 1867): 3063.262297405192, (8, 1868): 3061.8164858440095, (8, 1870): 3060.8475803323186, (8, 1871): 3063.1516198013933, (8, 1875): 3057.113310729247, (8, 1880): 3052.2434885745492, (8, 1882): 3052.5982825916763, (8, 1883): 3068.6953625605606, (8, 1889): 3054.25556777158, (8, 1893): 3061.1606643216764, (8, 1894): 3059.2566355841495, (8, 1899): 3052.718609362829, (8, 1900): 3054.3009287527775, (8, 1902): 3064.62479566579, (8, 1905): 3066.986244593973, (8, 1907): 3056.063217337067, (8, 1910): 3057.416162190863, (8, 1917): 3073.468483243742, (8, 1920): 3056.54416016939, (8, 1935): 3067.9643628947883, (8, 1937): 3070.0527239312064, (8, 1946): 3049.0105637764505, (8, 1949): 3051.6409942182404, (8, 1950): 3042.1665494635936, (8, 1951): 3046.5622340075456, (8, 1952): 3048.8606264499294, (8, 1953): 3050.9915264466995, (8, 1954): 3048.45719097284, (8, 1958): 3050.5945641567455, (8, 1960): 3054.5840372432704, (8, 1968): 3056.160024276252, (8, 1969): 3069.0922970284746, (8, 1974): 3065.6552391564915, (8, 1975): 3065.415295682644, (8, 1979): 3059.8321080570186, (8, 1980): 3058.7486843370957, (8, 1981): 3060.88527803108, (8, 1985): 3062.4974751329396, (8, 1994): 3037.3591588828017, (8, 2011): 3052.277939011109, (8, 2019): 3072.2467689594896, (8, 2020): 3069.602233806989, (8, 2029): 3058.9427116837596, (8, 2030): 3067.779028895879, (8, 2032): 3056.8799263088576, (8, 2033): 3062.85504305941, (8, 2034): 3062.444504106291, (8, 2036): 3050.5856658474154, (8, 2037): 3053.6728325696567, (8, 2038): 3056.053655822319, (8, 2042): 3087.5441986600717, (8, 2050): 3061.8900272164938, (8, 2051): 3061.099754266249, (8, 2053): 3062.083382160182, (8, 2054): 3064.85863540609, (8, 2066): 3059.151806590903, (8, 2067): 3059.3416287629884, (8, 2071): 3032.2589521210366, (8, 2072): 3037.74577095959, (8, 2073): 3024.1645962831967, (8, 2074): 3023.250701735745, (8, 2080): 3013.8675169371886, (8, 2082): 3040.631951086089, (8, 2083): 3043.488766954679, (8, 2089): 3037.939768557274, (8, 2090): 3040.658477750114, (8, 2092): 3037.3676905000634, (8, 2098): 3017.6712230241346, (8, 2099): 3020.5531300664065, (8, 2101): 3016.8434615165006, (8, 2102): 3031.580439456734, (8, 2103): 3026.8351794150217, (8, 2104): 3024.110085612006, (8, 2106): 3045.2051948601843, (8, 2112): 3018.547207045618, (8, 2113): 3033.5094850783985, (8, 2114): 3036.5853809613736, (8, 2117): 3047.1691349194043, (8, 2123): 3035.7775689592354, (8, 2124): 3038.817194620177, (8, 2134): 3029.5634035976996, (8, 2138): 3038.74500929305, (8, 2141): 3030.7999364561542, (8, 2148): 3032.8814617134317, (8, 2150): 3023.292020686262, (8, 2151): 3026.3212895182605, (8, 2152): 3021.4540067066414, (8, 2153): 3034.1383493060207, (8, 2154): 3021.697846752181, (8, 2155): 3019.8393098742667, (8, 2156): 3017.7896333469157, (8, 2157): 3019.4711981755486, (8, 2160): 3041.8740699040636, (8, 2161): 3020.6993112874798, (8, 2162): 3033.742980585157, (8, 2163): 3029.5567001263425, (8, 2164): 3029.121240801132, (8, 2168): 3023.3214898345836, (8, 2172): 3025.060246197778, (8, 2174): 3025.6614928481763, (8, 2178): 3027.226285080254, (8, 2179): 3025.1681537957907, (8, 2183): 3038.271118017346, (8, 2185): 3038.319832220569, (8, 2186): 3035.9694764162296, (8, 2190): 3042.7260358629687, (8, 2192): 3038.445420356806, (8, 2193): 3039.2028168339048, (8, 2194): 3034.828083412229, (8, 2195): 3033.8900821424513, (8, 2197): 3039.2315734773165, (8, 2205): 3032.673322929668, (8, 2207): 3024.234471805211, (8, 2208): 3028.8922896696986, (8, 2212): 3041.143828677344, (8, 2214): 2947.250888996868, (8, 2225): 2956.8593690973016, (8, 2231): 2942.708818894806, (8, 2278): 2998.3575402936485, (8, 2284): 3006.8033257704105, (8, 2285): 3005.2998362774415, (8, 2291): 2985.743700152526, (8, 2292): 2989.6517558048185, (8, 2307): 3000.8847256593663, (8, 2313): 2983.001221883079, (8, 2317): 2983.753142987685, (8, 2319): 2992.5683011656574, (8, 2321): 2996.3927619694377, (8, 2323): 2996.3930293712906, (8, 2326): 3013.187746239993, (8, 2327): 3009.2811980285787, (8, 2329): 3006.5592130273076, (8, 2330): 3003.3311349326054, (8, 2332): 3009.5122130555196, (8, 2344): 3000.325818598868, (8, 2346): 2999.7686212129697, (8, 2361): 3001.311644799796, (8, 2368): 3045.1519192478404, (8, 2374): 3049.1631198534064, (8, 2375): 3050.7880237557433, (8, 2377): 3036.0599186331347, (8, 2378): 3053.3339762532933, (8, 2379): 3053.332775096176, (8, 2380): 3055.0821726478516, (8, 2383): 3040.286733598597, (8, 2385): 3042.7314621711203, (8, 2395): 3043.317666471551, (8, 2397): 3051.3792926079973, (8, 2398): 3031.3259313549975, (8, 2399): 3036.886079037308, (8, 2400): 3035.6855856851985, (8, 2402): 3043.1855176597683, (8, 2403): 3046.503485949369, (8, 2404): 3047.5145353682565, (8, 2405): 3039.3776546641257, (8, 2407): 3046.232121414328, (8, 2408): 3049.9648760051805, (8, 2409): 3041.905325181486, (8, 2411): 3045.839677398065, (8, 2412): 3045.2098357046275, (8, 2413): 3047.8435190058435, (8, 2414): 3043.3312672565003, (8, 2422): 3044.604534114501, (8, 2424): 3046.2868990555517, (8, 2426): 3047.1359568298094, (8, 2433): 3040.6953101288445, (8, 2436): 3038.627483702468, (8, 2437): 3019.3482878112936, (8, 2440): 3023.7117669729987, (8, 2445): 3105.835033661065, (8, 2447): 3095.696826260971, (8, 2454): 3105.6312191235315, (8, 2455): 3106.5226940896473, (8, 2460): 3075.2209031555194, (8, 2461): 3079.0103816348374, (8, 2471): 3138.656464731194, (8, 2492): 3058.4122855493247, (8, 2511): 3030.199716020379, (8, 2523): 3044.5823192886883, (8, 2525): 3039.051454003439, (8, 2535): 3055.375145119672, (8, 2537): 3048.2882232660804, (8, 2538): 3053.5697866377004, (8, 2539): 3049.6200573739607, (8, 2540): 3058.540894183884, (8, 2542): 3062.9930314078747, (8, 2559): 3164.994105578251, (8, 2575): 3153.8194618263997, (8, 2599): 3010.6731483749822, (8, 2600): 3042.688022285406, (8, 2607): 3025.590365460115, (8, 2627): 3041.7801460359274, (8, 2647): 3058.377539226491, (8, 2674): 3051.4544540441943, (8, 2681): 3047.7934665045705, (8, 2683): 3057.1418432566397, (8, 2686): 3047.5562092616055, (8, 2689): 3164.3233377212046, (8, 2690): 3164.6134886234813, (8, 2713): 3178.782891754264, (8, 2714): 3179.569769145275, (8, 2715): 3182.525963989055, (8, 2739): 3180.256106540347, (8, 2740): 3164.908888813142, (8, 2741): 3166.6100852978107, (8, 2749): 3174.915543348653, (8, 2750): 3176.2640348973987, (8, 2752): 3178.5636856307183, (8, 2755): 3180.631109568546, (8, 2758): 3179.5918402113334, (8, 2759): 3179.793232515077, (8, 2769): 3176.847132617506, (8, 2771): 3168.8241489176985, (8, 2779): 3166.683138993452, (8, 2784): 3132.174023973786, (8, 2800): 3135.03728043344, (8, 2802): 3157.5809758283544, (8, 2803): 3156.839313205036, (8, 2804): 3155.020520351439, (8, 2805): 3158.91321385027, (8, 2807): 3159.115455287241, (8, 2809): 3157.156422587724, (8, 2812): 3139.2340969568127, (8, 2814): 3153.586184593387, (8, 2817): 3150.709375974897, (8, 2819): 3160.4416925752, (8, 2823): 3137.7206942183175, (8, 2832): 3162.0249242810632, (8, 2836): 3148.8191201848504, (8, 2839): 3159.463872263856, (8, 2841): 3153.157001878545, (8, 2843): 3152.8049870958425, (8, 2846): 3149.8587952020375, (8, 2849): 3163.4310737561013, (8, 2852): 3160.680368908207, (8, 2853): 3164.673102450124, (8, 2876): 3164.1895314262692, (8, 2877): 3174.5124618527893, (8, 2885): 3173.9563999775164, (8, 2918): 3164.374030814482, (8, 2921): 3168.4795877173437, (8, 2925): 3150.386151368858, (8, 2926): 3144.9961536171345, (8, 2930): 3155.1866674021867, (8, 2931): 3151.33822807436, (8, 2938): 3163.7763893797096, (8, 2940): 3180.067169269259, (8, 2947): 3165.321300858566, (8, 2949): 3156.5341183820224, (8, 2950): 3157.938220616391, (8, 2952): 3155.673403782238, (8, 2958): 3155.5002453002153, (8, 2959): 3158.407216877987, (8, 2960): 3163.1621775538865, (8, 2961): 3160.4665959031595, (8, 2963): 3153.225264684907, (8, 2968): 3154.271615364073, (8, 2976): 3153.0178000746496, (8, 2981): 3105.5660073002127, (8, 2982): 3103.5512502199144, (8, 2984): 3101.140400407179, (8, 3003): 3096.3553118656814, (8, 3046): 3075.845357793894, (8, 3050): 3094.735355698448, (8, 3051): 3096.7905279481706, (8, 3053): 3091.545317507676, (8, 3069): 3117.8102924627997, (8, 3071): 3092.0865102583493, (8, 3080): 3172.6623281099014, (8, 3199): 3084.255304400041, (8, 3200): 3078.4991797629355, (8, 3205): 3111.1354876485434, (8, 3209): 3081.1375806333276, (8, 3215): 3079.257854030942, (8, 3217): 3072.7094626648995, (8, 3249): 3080.3105238779435, (8, 3263): 3129.9543082482505, (8, 3289): 3097.150588858977, (8, 3301): 3097.602770264581, (8, 3302): 3095.656328673337, (8, 3307): 3092.8350141092346, (8, 3310): 3100.4205877627123, (8, 3391): 3083.8249069004864, (8, 3509): 2074.7321624772817, (8, 3510): 2070.1742789231585, (8, 3511): 2073.761753717098, (8, 3512): 2071.4242616256233, (8, 3514): 2072.817526177226, (8, 3519): 2082.707841617501, (8, 3536): 2083.7445246062975, (8, 3545): 2091.4540325925122, (8, 3548): 2085.177081927762, (8, 3572): 2085.6651100826994, (8, 3581): 2078.2963390204786, (8, 3583): 2077.468454100515, (8, 3601): 2090.404358695265, (8, 3656): 2080.8524090905603, (8, 3669): 2067.2345201344738, (8, 3670): 2071.119397862088, (8, 3695): 2049.7563550530635, (8, 3696): 2053.0666319003294, (8, 3782): 2096.058646466055, (8, 3792): 2089.6674763228407, (8, 3989): 126.49070165973694, (8, 4008): 100.9005547071302, (8, 4031): 96.2360516875218, (8, 4045): 111.27266523053248, (8, 4144): 117.86727888365307, (8, 4145): 152.74460415560193, (8, 4164): 129.7492659874557, (8, 4168): 142.16420318393693, (8, 4173): 146.18304336323502, (8, 4181): 161.02974802145803, (8, 4228): 165.78328569110604, (8, 4248): 185.08100823732659, (8, 4254): 365.6053826942136, (8, 4260): 359.76893791308635, (8, 4262): 354.74444353837487, (8, 4273): 353.13821595982427, (8, 4319): 462.53970898548107, (8, 4326): 463.9811997304809, (8, 4328): 461.37094011248547, (8, 4334): 460.6223437094181, (8, 4335): 463.64429485776907, (8, 4372): 1214.4375852518158, (8, 4413): 1253.5194066045233, (8, 4434): 1208.0708153156895, (8, 4447): 1192.7860901023116, (8, 4452): 1211.0289859619006, (8, 4463): 1298.1117185881399, (8, 4465): 1291.9360525257027, (8, 4619): 1311.270530835432, (8, 4645): 1302.3456834580406, (8, 4657): 1309.3570685847428, (8, 4666): 1315.6848954153336, (8, 4676): 1315.3238443970422, (8, 4678): 1311.9600571797127, (8, 4689): 1320.4338409862328, (8, 4704): 1321.1687017837191, (8, 4726): 1481.7166736946401, (8, 4727): 1479.2923676497524, (8, 4730): 1474.136867958063, (8, 4731): 1478.671264257681, (8, 4734): 1463.8147092878746, (8, 4735): 1464.1624575508667, (8, 4736): 1467.6081942106787, (8, 4737): 1466.6621902075103, (8, 4738): 1469.0526509477336, (8, 4756): 1472.8709209428505, (8, 4760): 1447.8946481240835, (8, 4761): 1444.0605515487214, (8, 4762): 1447.7704513680312, (8, 4765): 1450.625564662824, (8, 4773): 1483.945334138787, (8, 4774): 1485.9990991412894, (8, 4790): 1481.6988954232816, (8, 4795): 1478.5223745247645, (8, 4799): 1489.2805949570804, (8, 4801): 1500.128427319551, (8, 4804): 1474.058208676316, (8, 4805): 1471.5101183474912, (8, 4806): 1491.2921603373652, (8, 4815): 1492.6758435432698, (8, 4816): 1496.8310985571434, (8, 4817): 1502.8731765051223, (8, 4826): 1497.7674031166503, (8, 4830): 1496.394959171937, (8, 4839): 1455.1255377114426, (8, 4840): 1459.3698268681276, (8, 4841): 1456.0136377632512, (8, 4846): 1453.5259014610622, (8, 4848): 1457.2050643344096, (8, 4850): 1460.1000977153963, (8, 4871): 1413.1879730299643, (8, 4883): 1439.0414887793868, (8, 4900): 1419.7418019991296, (8, 4901): 1420.190946029863, (8, 4917): 1392.4538586494702, (8, 4931): 1382.9386509474446, (8, 4944): 1390.4743466350187, (8, 4956): 1387.7262845831162, (8, 4958): 1393.5122745176354, (8, 4959): 1395.8762690390506, (8, 4961): 1387.1626616237077, (8, 4966): 1388.9444724934074, (8, 5207): 1379.402791990368, (8, 5272): 1078.8293760858844, (8, 5283): 1081.174201212825, (8, 5287): 1098.8674478510309, (8, 5289): 1100.5040356494858, (8, 5293): 1065.8121961349905, (8, 5295): 1070.4855571429548, (8, 5296): 1078.8824826939717, (8, 5298): 1083.5264099469755, (8, 5303): 1092.2710926932486, (8, 5305): 1094.1325971114254, (8, 5306): 1104.7097970328216, (8, 5307): 1093.9860341834212, (8, 5308): 1097.6448971852521, (8, 5313): 1086.9923136818682, (8, 5314): 1084.890438666289, (8, 5317): 1103.1344658719988, (8, 5319): 1092.5267649741563, (8, 5324): 1085.062889168436, (8, 5326): 1079.7910021442915, (8, 5348): 1111.5313509539496, (8, 5351): 1124.5400515939778, (8, 5399): 1113.9349619841573, (8, 5413): 1145.455696498124, (8, 5422): 1106.55919550694, (8, 5445): 1106.1425991008593, (8, 5448): 1104.6449250399435, (8, 5456): 1113.20862908968, (8, 5467): 1116.9831656983254, (8, 5624): 1076.0239205991866, (8, 5671): 1013.854545307722, (8, 5672): 1009.3190433917946, (8, 5797): 1069.573482417371, (8, 5871): 1224.3607402203802, (8, 5976): 1201.9438995757441, (8, 6118): 2586.7025076520235, (8, 6248): 2670.518691150158, (8, 6345): 1019.256647107344, (8, 6352): 1039.2328918830146, (8, 6354): 1014.8808479064375, (8, 6359): 1010.1104261034875, (8, 6376): 1034.190044542879, (8, 6378): 1017.1327729171907, (8, 6381): 1011.1477838159491, (8, 6383): 1023.8099065644658, (8, 6396): 1010.2752106640369, (8, 6399): 1018.010714415837, (8, 6408): 1039.2986101999875, (8, 6409): 1032.1561823580541, (8, 6419): 1067.7117006785488, (8, 6422): 1038.393913532892, (8, 6423): 1040.12160525116, (8, 6424): 1019.4388101857917, (8, 6439): 1023.9820833751038, (8, 6464): 1030.174428980577, (8, 6465): 1031.3273916675812, (8, 6469): 1027.1892174194215, (8, 6470): 1028.0272832211854, (8, 6472): 1003.0610905064126, (8, 6480): 1011.0690872321533, (8, 6486): 1004.0924105981471, (8, 6497): 1006.5667545246729, (8, 6503): 1033.8785863753285, (8, 6508): 1029.7427513151251, (8, 6509): 1027.226607058961, (8, 6521): 1010.4792308155869, (8, 6544): 1014.486787840536, (8, 6552): 1039.1235949216893, (8, 6553): 1042.4333791582083, (8, 6554): 1045.7683669623623, (8, 6578): 1033.227928314204, (8, 6582): 1038.2975086416704, (8, 6601): 1032.2745824652395, (8, 6609): 1003.5183825301337, (8, 6610): 1003.1443382197735, (8, 6611): 1001.1083235731198, (8, 6614): 1001.9848089212009, (8, 6615): 1001.8568878558592, (8, 6616): 1000.2986741064158, (8, 6617): 1001.1258827985253, (8, 6618): 998.2776853388946, (8, 6619): 1004.608106265239, (8, 6620): 1001.127795416182, (8, 6621): 1004.0494410057913, (8, 6622): 1002.7845486762519, (8, 6623): 1003.1976209835333, (8, 6624): 1006.5458090909474, (8, 6625): 1006.5976388668716, (8, 6626): 1004.4003506822257, (8, 6627): 1001.945726960108, (8, 6628): 1002.62948804075, (8, 6629): 1006.8633208174933, (8, 6630): 1007.62480847315, (8, 6632): 1006.6521125918886, (8, 6634): 1011.1342549899676, (8, 6635): 1004.5468616552381, (8, 6636): 1000.4535574906816, (8, 6637): 1010.7276162791501, (8, 6638): 1008.0773797405784, (8, 6639): 1002.1378378645273, (8, 6640): 1007.1914156905, (8, 6641): 1004.8359431327403, (8, 6642): 1008.5764103830389, (8, 6643): 1004.1314826701887, (8, 6645): 1004.6030322263142, (8, 6646): 998.5425662426352, (8, 6647): 1007.4325582114008, (8, 6653): 1001.7230808099393, (8, 6655): 1001.8395117408338, (8, 6658): 1011.6637047925524, (8, 6662): 1009.3491824003663, (8, 6819): 1178.0899957578156, (8, 6996): 1140.0912890772447, (8, 7059): 1103.6563458690018, (8, 7187): 1211.7803841120417, (8, 7304): 1259.5575944964394, (8, 7528): 1161.1930990339997, (8, 7720): 934.5934973514362, (8, 7793): 947.6149265971006, (8, 7807): 941.8745135880029, (8, 7808): 950.743187833259, (8, 7831): 990.1025211775765, (8, 7850): 950.1825431368918, (8, 7852): 956.8814137591432, (8, 8012): 933.2985311844054, (8, 8125): 973.5497714485648, (8, 8208): 873.1083610899012, (8, 8392): 982.4343477224767, (8, 8651): 1359.510928627647, (8, 9088): 1177.8123793236255, (8, 9443): 1494.6637054564935, (8, 9444): 1490.471611174979, (8, 9828): 1681.8435905618194, (8, 9868): 1661.2568401177912, (8, 10180): 976.3193253986826, (8, 10256): 905.6354398927296, (8, 10276): 926.3671747961813, (8, 10378): 882.740848140542, (8, 10676): 1057.3300988747878, (8, 10714): 1121.4620925974946, (8, 10730): 1071.471473199186, (8, 10862): 1606.7025318716308, (8, 10881): 1603.358412007862, (8, 10883): 1606.0678694008136, (8, 10885): 1606.8481990833473, (8, 10891): 1610.3359695232325, (8, 10909): 1605.0494538178962, (8, 10911): 1598.8533966683924, (8, 10913): 1601.475305175222, (8, 10915): 1598.5594433442752, (8, 10919): 1595.6122929761536, (8, 11037): 1688.9047870446288, (8, 11039): 1674.2482921777282, (8, 11516): 240.744302085132, (8, 11856): 459.0804157468298, (8, 11857): 469.96672502796673, (8, 11861): 464.6066903457406, (8, 11881): 456.8368940056775, (8, 11902): 468.61817529957426, (8, 11911): 463.20725280489, (8, 11914): 464.80884687998713, (8, 11922): 458.6230374300827, (8, 11924): 453.8299462508876, (8, 11926): 456.7710772567698, (8, 11950): 441.4892749825035, (8, 11963): 431.62875671702443, (8, 11983): 425.3149813404297, (8, 11985): 427.567265248793, (8, 12009): 417.53452276981983, (8, 12010): 427.58819577442796, (8, 12018): 424.826730945592, (8, 12020): 424.5362461866218, (8, 12021): 422.05403555979535, (8, 12024): 415.2303623109541, (8, 12025): 419.95624805279107, (8, 12027): 420.95403866632887, (8, 12031): 428.8809000451733, (8, 12032): 428.29281501935975, (8, 12035): 415.3011251965557, (8, 12041): 434.05436213494727, (8, 12045): 528.6532490570663, (8, 12145): 465.5882445557018, (8, 12275): 105.36039026014915, (8, 12294): 132.35739051891449, (8, 12358): 44.16563792910995, (8, 12463): 29.337578366121978, (8, 12465): 30.916554380620767, (8, 12482): 11.306505319050329, (8, 12503): 14.85235183081815, (8, 12506): 15.62535885111533, (8, 12549): 6.183288209585149, (8, 12559): 3.9986765956631007, (8, 12569): 5.799826868230741, (8, 12572): 5.2840379411262415, (8, 12574): 6.100179661439792, (8, 12576): 10.099550738082788, (8, 12591): 22.06924268546257, (8, 12608): 46.91611378521322, (8, 12696): 37.52210054009205, (8, 12710): 59.43181623286666, (8, 12728): 37.3547859689427, (8, 12766): 685.0812544315177, (8, 12771): 714.1089982560368, (8, 12790): 718.2932197785916, (8, 12795): 728.0509365593001, (8, 12797): 767.7526931406361, (8, 12798): 762.2833817460039, (8, 12811): 730.3836422612989, (8, 12830): 741.0646752620058, (8, 12848): 735.5977638242163, (8, 12850): 733.1259036735827, (8, 12852): 742.5750520647221, (8, 12854): 747.4660125609047, (8, 12859): 730.8050513413273, (8, 12861): 756.9077516100995, (8, 12865): 724.3873052408693, (8, 12866): 726.890902160276, (8, 12867): 717.1116832642076, (8, 12874): 721.8524341156274, (8, 12875): 718.1495361050339, (8, 12881): 733.3325477635112, (8, 12883): 727.2869731180019, (8, 12885): 714.9423475240201, (8, 12888): 730.0754713457819, (8, 12889): 731.4422869389064, (8, 12892): 720.8125697509155, (8, 12893): 729.8660089394283, (8, 12896): 726.9403207738218, (8, 12906): 721.7041970551693, (8, 13018): 770.8966721160368, (8, 13071): 772.7048523638882, (8, 13131): 805.0232457062891, (8, 13146): 772.4781325790286, (8, 13159): 823.8339939635517, (8, 13193): 811.0703603772844, (8, 13198): 867.2078338996776, (8, 13292): 802.529727967916, (8, 13296): 785.4125086873511, (8, 13406): 902.8883274080541, (8, 13407): 904.8832352253158, (8, 13417): 910.9059812405233, (8, 13418): 905.2401975429074, (8, 13438): 878.96578899714, (8, 13442): 873.5619235284942, (8, 13443): 878.3629761408135, (8, 13764): 1315.8654182639864, (8, 13766): 1309.6665655116415, (8, 13771): 1317.686403529913, (8, 13783): 1317.9414742920874, (8, 13784): 1302.082325357803, (8, 13792): 1332.7551902244977, (8, 13824): 1322.5537354413789, (8, 14017): 1277.09716559772, (8, 14870): 1488.7255877786106, (8, 14997): 1241.7949543626191, (8, 15000): 1242.8153548219673, (8, 15003): 1240.6670293284906, (8, 15006): 1225.2886984357115, (8, 15007): 1221.6383908466491, (8, 15056): 1226.870833348036, (8, 15063): 1231.2031763199236, (8, 15069): 1234.3221651765193, (8, 15076): 1222.1408035024742, (8, 15086): 1232.131742911159, (8, 15087): 1238.3859966265816, (8, 15111): 1248.3299006925488, (8, 15116): 1242.7656406748147, (8, 15722): 1343.4564758399736, (8, 15998): 1451.9854305758467, (8, 16073): 2193.5855405389298, (8, 16939): 2792.7427201553724, (8, 16940): 2786.975293436827, (8, 16951): 2792.2686618989314, (8, 16963): 2793.1384406451516, (8, 16965): 2800.716663159716, (8, 16969): 2798.2109302263307, (8, 16970): 2796.129361042149, (8, 16971): 2789.348091856161, (8, 16973): 2788.43431938371, (8, 16974): 2803.323794787774, (8, 16976): 2796.9441281882036, (8, 16978): 2792.1499007587286, (8, 16980): 2799.8375612116183, (8, 16982): 2802.7914356752203, (8, 17045): 2966.2608630206482, (8, 17048): 2974.706592150168, (8, 17304): 232.70379531137556, (8, 17305): 229.19321022440758, (8, 17330): 227.9785441632938, (8, 17334): 240.70861841729385, (8, 17343): 221.46288642749536, (8, 17345): 233.7049952464081, (8, 17347): 223.81268759110233, (8, 17351): 249.95006733453107, (8, 17372): 238.66622900145032, (8, 17373): 222.99067175215765, (8, 17377): 221.28414171042672, (8, 17382): 229.9593727417792, (8, 17383): 230.79419905976917, (8, 17389): 235.31405666011, (8, 17400): 227.73254488291352, (8, 17401): 229.10339009235705, (8, 17402): 226.50030660023558, (8, 17403): 225.03648980031866, (8, 17440): 225.88062493878718, (8, 17455): 218.2563201641705, (8, 17491): 212.3972061394538, (8, 17507): 264.1047676620279, (8, 17509): 262.06807126158554, (8, 17590): 245.3429325760809, (8, 17615): 319.26342129729426, (8, 17642): 310.7944347731784, (8, 17643): 307.90555226583007, (8, 17668): 321.5128750580805, (8, 17721): 350.3053849646353, (8, 17754): 321.1640393237581, (8, 17769): 272.5443775598201, (8, 17776): 274.3136079225626, (8, 17804): 267.6865437988129, (8, 17809): 263.8122142051242, (8, 17824): 272.19144393952587, (8, 17837): 258.3725298335177, (8, 17838): 253.52200278556356, (8, 17862): 254.7712283016917, (8, 17866): 247.4824042497604, (8, 17872): 260.5042329174892, (8, 17873): 265.3374930001842, (8, 17881): 257.3882109900197, (8, 17947): 2324.725123337978, (8, 17951): 2312.985632681713, (8, 17953): 2310.9679370340923, (8, 17954): 2311.936109943114, (8, 17959): 2321.926008645583, (8, 17963): 2317.390550832526, (8, 18000): 2258.287285291607, (8, 18001): 2260.952530842892, (8, 18111): 2434.841242519622, (8, 18148): 2141.1741739756058, (8, 18166): 2255.981040748839, (8, 18189): 2360.692168301658, (8, 18239): 223.59990849447416, (8, 18240): 222.81490473339423, (8, 18245): 222.7538092771765, (8, 18247): 222.83240818971262, (8, 18251): 221.75412470944957, (8, 18256): 219.61943081539042, (8, 18258): 220.26100458254572, (8, 18259): 219.61941966625008, (8, 18260): 218.57108060156358, (8, 18262): 217.17776834360845, (8, 18263): 218.85730206738097, (8, 18264): 217.86291428307817, (8, 18266): 216.12502103125217, (8, 18267): 215.27305477280945, (8, 18268): 214.55526590699063, (8, 18269): 212.776655855319, (8, 18275): 213.61175476369417, (8, 18285): 218.52544841846736, (8, 18308): 237.5381380964307, (8, 18313): 241.58440556981313, (8, 18314): 237.06148625546564, (8, 18315): 215.09167738777063, (8, 18316): 214.12893937708685, (8, 18317): 213.2271130313892, (8, 18320): 213.9422569461352, (8, 18321): 212.9555753682704, (8, 18322): 211.75251034448692, (8, 18324): 212.31770275431455, (8, 18325): 210.08259885209804, (8, 18326): 210.96537891147352, (8, 18327): 211.51190906830948, (8, 18329): 210.31707685291164, (8, 18330): 208.03250678739974, (8, 18331): 210.06348126759755, (8, 18332): 211.6015815630269, (8, 18333): 209.22481611823258, (8, 18336): 212.11144968782756, (8, 18337): 212.0578981832015, (8, 18403): 207.17656200907103, (8, 18432): 215.9674960694191, (8, 18451): 208.1454288079571, (8, 18466): 210.83675817396056, (8, 18481): 217.4471293302859, (8, 18483): 216.65490819807223, (8, 18484): 218.48517027440124, (8, 18485): 224.81600683969995, (8, 18486): 224.49507866802878, (8, 18487): 228.31501550970026, (8, 18489): 222.03411801568453, (8, 18490): 221.46689139108696, (8, 18491): 220.14972606345015, (8, 18492): 230.44044352488388, (8, 18493): 225.96610996343708, (8, 18494): 221.9169755851072, (8, 18495): 222.5748113389164, (8, 18496): 223.27517421542743, (8, 18497): 229.97362750457728, (8, 18498): 225.93572068683628, (8, 18499): 223.56063394023337, (8, 18501): 226.74300459120565, (8, 18502): 228.35625965516843, (8, 18503): 228.58445612964059, (8, 18504): 221.70761230940892, (8, 18506): 228.93807341793013, (8, 18507): 230.95904594345228, (8, 18508): 224.69396792464457, (8, 18509): 225.45403883801285, (8, 18510): 229.70567147934204, (8, 18511): 227.24681052594443, (8, 18512): 227.40962725301566, (8, 18515): 222.74110524312042, (8, 18516): 225.39391022687715, (8, 18517): 228.65342243643602, (8, 18518): 223.40683870836304, (8, 18519): 220.90722989703607, (8, 18520): 224.15252179827235, (8, 18522): 212.96326736229747, (8, 18523): 213.55072575529192, (8, 18532): 212.85002161892464, (8, 18535): 215.2461498293959, (8, 18537): 216.60520150441934, (8, 18539): 216.78232588926366, (8, 18540): 217.1165199565481, (8, 18541): 216.86505467222992, (8, 18542): 216.62457819035683, (8, 18543): 218.21363875435893, (8, 18546): 218.98300334339896, (8, 18555): 217.0101487886981, (8, 18556): 217.29146386022398, (8, 18565): 214.23871675745136, (8, 18567): 215.5025863429876, (8, 18568): 215.7722241903003, (8, 18577): 208.08037863153302, (8, 18583): 206.64015396838167, (8, 18605): 201.846866835787, (8, 18608): 218.67885346401874, (8, 18616): 195.1666465513439, (8, 18618): 191.98027989900984, (8, 18625): 185.9221125641028, (8, 18645): 188.04490796892856, (8, 18646): 189.00332142115803, (8, 18653): 200.75786275435604, (8, 18654): 196.5363240094494, (8, 18655): 200.78253833349632, (8, 18666): 171.1822404310372, (8, 18837): 156.28728732490413, (8, 18974): 194.73769016956115, (8, 18999): 181.40535309440824, (8, 19000): 178.38296172439416, (8, 19174): 333.0954538523519, (8, 19342): 272.42048485266855, (8, 19455): 303.3369014833409, (8, 19555): 467.8563816267426, (8, 19564): 462.025287540601, (8, 19573): 467.9763578920818, (8, 19586): 470.3998332796346, (8, 19605): 467.10095271108844, (8, 19611): 462.74423784921595, (8, 19614): 463.7378678257789, (8, 19641): 386.23954374924637, (8, 19702): 389.5210657957718, (8, 19713): 394.6462973124868, (8, 19731): 494.8449492947918, (8, 19819): 327.47369066470884, (8, 19893): 768.2372310138252, (8, 19899): 778.7416151333912, (8, 19929): 763.4997017930623, (8, 19951): 761.4145904442449, (8, 19962): 776.6509080555822, (8, 19970): 747.4814478844849, (8, 19971): 753.94125797795, (8, 19972): 759.1425154798557, (8, 19975): 754.8653656450952, (8, 19978): 730.8092919396934, (8, 19987): 726.2092641495002, (8, 19989): 726.3785939000599, (8, 20039): 724.0066265116885, (8, 20043): 717.7411194034545, (8, 20047): 711.9984511765666, (8, 20052): 717.4316134590549, (8, 20054): 720.3420450978307, (8, 20085): 681.1100809551075, (8, 20104): 680.354192494606, (8, 20132): 692.6127016682506, (8, 20203): 827.7966695886493, (8, 20280): 847.9262560751896, (8, 20285): 856.2524258598085, (8, 20290): 843.7768838660908, (8, 20297): 843.0832364847241, (8, 20309): 779.9597302202502, (8, 20453): 739.9823112802482, (8, 20485): 842.7505305748019, (8, 20520): 842.097110874228, (8, 20526): 862.2477475900378, (8, 20698): 1530.8824603853025, (8, 20868): 1751.5376141214792, (8, 21042): 763.8748638799256, (8, 21057): 720.1476023476214, (8, 21066): 744.883418729123, (8, 21075): 748.3740363101385, (8, 21093): 765.1742174367577, (8, 21098): 741.5885910030058, (8, 21127): 762.6894260302201, (8, 21130): 756.7641809015419, (8, 21144): 753.6339362474989, (8, 21146): 765.5130903358232, (8, 21147): 753.099671219661, (8, 21148): 747.0259163750931, (8, 21153): 750.2484884137085, (8, 21293): 698.0575547544097, (8, 21426): 675.4350140384572, (8, 21442): 625.184291137083, (8, 21451): 620.4644296005274, (8, 21466): 651.3636817353306, (8, 21469): 644.8764776476739, (8, 21471): 654.6151976278039, (8, 21473): 649.4939096644515, (8, 21475): 654.34382040402, (8, 21482): 639.9565723684494, (8, 21484): 641.7382042816797, (8, 21488): 645.3239800251206, (8, 21494): 655.5596442013173, (8, 21498): 650.4347026758705, (8, 21500): 659.5290170199492, (8, 21514): 651.4102956728608, (8, 21537): 663.9965273029877, (8, 21662): 649.9724318563041, (8, 21691): 675.9128144785863, (8, 21757): 712.0567598172819, (8, 21777): 862.0352655613135, (8, 21778): 868.3518776206237, (8, 21779): 867.2100277543218, (8, 21790): 852.3719747813504, (8, 21802): 857.3764693284286, (8, 21824): 853.3049734219577, (8, 21874): 868.580698779866, (8, 21879): 876.8844911139302, (8, 21983): 826.5227070700586, (8, 22002): 774.8444165949282, (8, 22132): 772.5716184719593, (8, 22261): 1772.3706001440926, (8, 22298): 1761.3572071619285, (8, 22339): 1848.2018777692256, (8, 22508): 1638.4967098452603, (8, 22841): 2997.1207477653384, (8, 22842): 2997.890536855182, (8, 22874): 2984.1196181267146, (8, 22941): 2983.2872760026976, (8, 22956): 2993.871430039068, (8, 22960): 2995.038332108062, (8, 22968): 3014.7954455588047, (8, 22970): 3016.1151099734047, (8, 22974): 3027.150269980409, (8, 22980): 3039.187449374113, (8, 23025): 3046.562898956544, (8, 23028): 3045.6174649459326, (8, 23081): 3076.134788003501, (8, 23104): 3067.978429588365, (8, 23147): 2938.626754826503, (8, 23298): 548.652696513784, (8, 23376): 567.9183929574887, (8, 23381): 590.3908483653244, (8, 23529): 545.6303943549206, (8, 23556): 555.1276688808965, (8, 23718): 552.4961594912068, (8, 24001): 432.94179751807695, (8, 24094): 421.53426490842764, (8, 24129): 403.62290606179954, (8, 24174): 451.62363600552914, (8, 24235): 420.67401315628075, (8, 24259): 396.15514470119166, (8, 24260): 398.62113069799534, (8, 24261): 401.14074489010767, (8, 24305): 373.2294069232249, (8, 24306): 371.643503976107, (8, 24307): 375.5996876452117, (8, 24308): 373.90151399633197, (8, 24498): 305.75585701949063, (8, 24499): 305.9301155863751, (8, 24500): 308.5499422360481, (8, 24668): 306.97192414993583, (8, 24711): 298.4157603318717, (8, 24756): 300.3567481189528, (8, 24788): 290.49988521018986, (8, 24809): 320.52084807660253, (8, 24813): 310.0625035404135, (8, 24821): 313.001715281955, (8, 24825): 312.970058113427, (8, 24832): 320.84174294204325, (8, 24833): 317.49435772940325, (8, 24835): 314.8177907009841, (8, 24837): 307.97167299686237, (8, 24840): 322.1407502666206, (8, 24841): 315.35100692916, (8, 24844): 323.0501543913652, (8, 24845): 315.8754276840761, (8, 24846): 322.0040033574966, (8, 24849): 320.7078698059412, (8, 24850): 310.33188498640766, (8, 24863): 350.0795589591892, (8, 24866): 343.61532333409167, (8, 24885): 339.6670626045525, (8, 24886): 341.31139457280665, (8, 24889): 320.2345346299126, (8, 24903): 311.7283115912228, (8, 24909): 329.3011557610094, (8, 24999): 44.73518365524526, (8, 25019): 39.76893249722001, (8, 25028): 50.22045174212155, (8, 25137): 926.8028657585749, (8, 25145): 922.4580645347296, (8, 25208): 955.0059037722062, (8, 25233): 962.0968067388693, (8, 25371): 877.7682582856276, (8, 25377): 875.8059326074292, (8, 25828): 1108.3201094931267, (8, 25851): 1129.3992129574385, (8, 25874): 1094.5799912558703, (8, 25898): 1099.2614483152597, (8, 25946): 1111.2461350969766, (8, 26047): 1074.8700958134593, (8, 26066): 863.0637049688307, (8, 26197): 980.1611041314975, (8, 26212): 1322.2688630079447, (8, 26253): 1343.7380749029867, (8, 26254): 1334.0363340058352, (8, 26257): 1331.4124536746374, (8, 26258): 1340.8366627582639, (8, 26260): 1335.6234816392612, (8, 26266): 1332.7666583437986, (8, 26267): 1328.2713631161625, (8, 26271): 1329.4173086969604, (8, 26304): 1249.0199486140339, (8, 26305): 1246.1353442563604, (8, 26363): 1150.0047002425144, (8, 26441): 1824.4070752729033, (8, 26442): 1822.1831503914104, (8, 26450): 1811.3307721553447, (8, 26459): 1810.466648143611, (8, 26462): 1811.9732649903335, (8, 26467): 1843.8205814196438, (8, 26471): 1834.904370991506, (8, 26472): 1833.961325993767, (8, 26473): 1833.5970441157344, (8, 26476): 1828.5102173787245, (8, 26485): 1815.8810558902626, (8, 26493): 1816.2184913079748, (8, 26524): 1816.7368641059204, (8, 26525): 1815.496453267453, (8, 26556): 1830.596940059483, (8, 26560): 1829.521630089805, (8, 26561): 1822.6304906619896, (8, 26564): 1827.6631870373722, (8, 26569): 1820.9651049664615, (8, 26570): 1818.2369393490715, (8, 26573): 1820.011992597025, (8, 26581): 1819.7900271252533, (8, 26583): 1817.39436423395, (8, 26593): 1819.901113457829, (8, 26837): 1846.0113016680202, (8, 26844): 1853.271101364175, (8, 26863): 1837.5348684962005, (8, 26893): 1858.4603581803442, (8, 26902): 1868.3240106240785, (8, 26905): 1858.2767233893999, (8, 26912): 1865.9964919250654, (8, 26921): 1847.5543608854891, (8, 26922): 1827.8680077492936, (8, 27212): 1889.7275350255068, (8, 27218): 1880.4633997747999, (8, 27239): 1903.8779018403318, (8, 27257): 1896.7094798431692, (8, 27274): 1906.8146999991516, (8, 27279): 1905.4039047885694, (8, 27282): 1897.117282636986, (8, 27283): 1900.0858846658255, (8, 27285): 1910.6600039024272, (8, 27286): 1903.3327431100115, (8, 27290): 1890.0592107132754, (8, 27295): 1884.7211462240095, (8, 27300): 1908.1823239793505, (8, 27344): 1886.6868990049647, (8, 27366): 1896.210621822943, (8, 27383): 1911.7016192376284, (8, 27398): 1921.4395294004744, (8, 27406): 1913.0845268257333, (8, 27407): 1915.4061984101163, (8, 27426): 1903.4182127257566, (8, 27432): 1867.9156108278232, (8, 27460): 1889.9947263544345, (8, 27523): 1901.0307477921301, (8, 27545): 2045.6179678487683, (8, 27602): 2235.097325837825, (8, 27606): 2238.373748957257, (8, 27646): 2043.7937156306057, (8, 27667): 2081.5501227803175, (8, 27672): 2083.4455888331527, (8, 27674): 2077.062341898091, (8, 27688): 2082.1118270454126, (8, 27692): 2090.0716507079187, (8, 27693): 2084.4376796457027, (8, 27705): 2084.2347814548943, (8, 27712): 2087.0829771656654, (8, 27786): 2237.2277073453565, (8, 27790): 2212.956730031607, (8, 27791): 2210.710877952559, (8, 27795): 2226.82280331275, (8, 27801): 2209.0544017998895, (8, 27813): 2243.384457261349, (8, 27816): 2235.9205358401373, (8, 27823): 2208.3517850306303, (8, 27830): 2226.89230663435, (8, 27884): 1981.7742275030987, (8, 27885): 2028.0932711154755, (8, 27896): 2000.0556872408265, (8, 27919): 1998.0397652427455, (8, 27922): 2003.936730616662, (8, 27930): 1988.7108937654546, (8, 27934): 1990.5631074961123, (8, 27935): 1991.9611767808249, (8, 27948): 2219.9982554979238, (8, 27951): 2229.5029943623276, (8, 28061): 2032.1233645688228, (8, 28290): 2431.9112745032835, (8, 28292): 2438.842752886164, (8, 28293): 2433.1691853230313, (8, 28295): 2428.9886457791645, (8, 28296): 2431.0963479957736, (8, 28297): 2428.1335781854687, (8, 28302): 2424.582712596116, (8, 28310): 2466.3159168810407, (8, 28313): 2468.778446109488, (8, 28372): 2476.8227306936246, (8, 28398): 2476.941090016829, (8, 28399): 2473.9127858331435, (8, 28400): 2477.923832910644, (8, 28401): 2468.2628019611716, (8, 28445): 2462.8099720119717, (8, 28475): 2464.9816763247377, (8, 28885): 477.2973513649591, (8, 28886): 482.6260698640738, (8, 28915): 490.8365597175623, (8, 28916): 489.7105071529125, (8, 28917): 493.4634506498582, (8, 28921): 469.9364550564991, (8, 28931): 473.457829410684, (8, 28945): 522.8281088078821, (8, 28982): 507.508517745918, (8, 29219): 555.5023988017184, (8, 29228): 562.4213119694786, (8, 29246): 561.0352292358358, (8, 29248): 575.1018951964929, (8, 29282): 575.7599751383198, (8, 29290): 545.1785877707498, (8, 29291): 549.6702609526882, (8, 29292): 547.4349344443414, (8, 29293): 548.2873039732392, (8, 29294): 553.4241287307318, (8, 29298): 551.8233039900205, (8, 29299): 555.5661464902508, (8, 29304): 548.4229296377811, (8, 29317): 546.8085156862709, (8, 29323): 546.3297672139851, (8, 29330): 547.5480322645178, (8, 29331): 545.2495543590552, (8, 29344): 579.7507956099769, (8, 29445): 719.1787570902404, (8, 29724): 2934.8804860988807, (8, 29738): 2938.145862819848, (8, 29745): 2927.2635792458177, (8, 29748): 2922.235855651723, (8, 29750): 2924.6464877237318, (8, 29759): 2918.611602274805, (8, 29772): 2930.562881942611, (8, 29781): 2927.754424931442, (8, 29784): 2928.6752304680713, (8, 29790): 2929.136264933085, (8, 29811): 2919.252404437677, (8, 29817): 2923.0560501582186, (8, 29818): 2920.198038529926, (8, 29929): 2930.404139541274, (8, 30039): 2991.7137599699017, (8, 30066): 2974.8390637933135, (8, 30116): 2849.6332473771195, (8, 30238): 2665.365339718029, (8, 30248): 2775.0571937630407, (8, 30260): 2778.7591175725606, (8, 30545): 486.51449471588495, (8, 30733): 618.8673846587837, (8, 30756): 693.3334229513389, (8, 30921): 607.0521985774396, (8, 31079): 997.3962941029131, (8, 31149): 1010.0748970461264, (8, 31154): 1010.9983594613986, (8, 31160): 1011.2179376174769, (8, 31163): 1013.6682760550436, (8, 31189): 1082.0318573277425, (8, 31215): 1078.9133283184992, (8, 31259): 1093.5025483132545, (8, 31262): 1100.3783122955758, (8, 31430): 997.1507219990409, (8, 31568): 1202.845061296427, (8, 31751): 1038.7997138021528, (11, 109): 414.01123141586527, (11, 872): 2093.38779596826, (11, 873): 2101.877203367874, (11, 877): 2099.506037315263, (11, 879): 2100.844501536225, (11, 884): 2094.1382426801056, (11, 889): 2099.0705790074717, (11, 891): 2091.1112637099695, (11, 892): 2107.256524474818, (11, 894): 2105.851899088476, (11, 896): 2096.3216540414987, (11, 903): 2100.7541574137344, (11, 909): 2083.629941191514, (11, 910): 2086.2742827519514, (11, 912): 2080.8372071463946, (11, 913): 2075.124645408789, (11, 916): 2071.6021439721103, (11, 926): 2088.0670727318884, (11, 927): 2085.048036151112, (11, 948): 2087.903451577671, (11, 961): 2089.528136902472, (11, 962): 2089.9650664537094, (11, 963): 2090.6261063030584, (11, 967): 2104.0123789762665, (11, 974): 2101.358353647688, (11, 998): 2108.039975638043, (11, 1014): 2283.8261661471333, (11, 1086): 2050.4267326523322, (11, 1087): 2046.6102596936823, (11, 1089): 2040.2305664660194, (11, 1090): 2044.0285417743348, (11, 1092): 2056.2506068673665, (11, 1097): 2047.4707386800706, (11, 1107): 2060.597801830642, (11, 1387): 769.5313538950812, (11, 1554): 656.3689476386453, (11, 1827): 2496.9225565263155, (11, 1828): 2497.4858902057267, (11, 1829): 2499.0153033989823, (11, 1830): 2499.252958917872, (11, 1831): 2499.731827561394, (11, 1832): 2498.666712808295, (11, 1833): 2498.4979501786793, (11, 1836): 2497.2153756727475, (11, 1841): 2503.046220935726, (11, 1843): 2500.7702170928815, (11, 1844): 2502.0523248845648, (11, 1845): 2499.5787952878727, (11, 1847): 2490.0112695419816, (11, 1848): 2493.1299090937973, (11, 1849): 2508.0119791211923, (11, 1850): 2509.292502051784, (11, 1851): 2496.2373678007807, (11, 1852): 2497.0885588610145, (11, 1854): 2498.0876184604645, (11, 1856): 2490.3967605258913, (11, 1857): 2493.258779697465, (11, 1858): 2506.1586801217722, (11, 1861): 2499.358257487257, (11, 1866): 2490.739276540429, (11, 1867): 2502.6754722152878, (11, 1868): 2500.3362547333586, (11, 1870): 2502.6067827533993, (11, 1871): 2501.7357193066287, (11, 1875): 2497.507921574603, (11, 1880): 2491.7795231499226, (11, 1882): 2493.5885666421063, (11, 1883): 2508.701367566201, (11, 1889): 2492.3450938928277, (11, 1893): 2498.157701752112, (11, 1894): 2495.8240254216103, (11, 1899): 2490.015229674928, (11, 1900): 2491.3887240960207, (11, 1902): 2501.895958327784, (11, 1905): 2505.0850189250423, (11, 1907): 2494.5731859187026, (11, 1910): 2494.822953095051, (11, 1917): 2508.885153792575, (11, 1920): 2494.2287333440618, (11, 1935): 2504.2584349956815, (11, 1937): 2506.831943604809, (11, 1946): 2483.806663873297, (11, 1949): 2486.1127941483815, (11, 1950): 2478.479215588065, (11, 1951): 2482.5106415751034, (11, 1952): 2487.4708366875393, (11, 1953): 2487.4094423921015, (11, 1954): 2486.4187280012898, (11, 1958): 2486.048685920358, (11, 1960): 2490.9115893805365, (11, 1968): 2492.8266569174098, (11, 1969): 2503.577020958707, (11, 1974): 2500.8762048285575, (11, 1975): 2501.2536965487257, (11, 1979): 2494.167389179969, (11, 1980): 2494.91179654971, (11, 1981): 2495.9661417007437, (11, 1985): 2497.1313495151308, (11, 1994): 2477.7594538371986, (11, 2011): 2493.897440884822, (11, 2019): 2517.5961221003818, (11, 2020): 2514.472365381157, (11, 2029): 2503.80975784271, (11, 2030): 2512.2877637019033, (11, 2032): 2502.6866136644508, (11, 2033): 2507.744205412964, (11, 2034): 2508.250653199066, (11, 2036): 2499.895972186397, (11, 2037): 2501.93750783679, (11, 2038): 2500.031689870125, (11, 2042): 2534.1061882300023, (11, 2050): 2505.3271912468817, (11, 2051): 2505.489980486515, (11, 2053): 2506.107094571048, (11, 2054): 2509.1443496658208, (11, 2066): 2503.0786543246304, (11, 2067): 2502.7630396638483, (11, 2071): 2471.753849932583, (11, 2072): 2476.8765444092382, (11, 2073): 2459.787173011142, (11, 2074): 2459.4483845732275, (11, 2080): 2451.0447827458606, (11, 2082): 2479.787022718881, (11, 2083): 2482.396183004744, (11, 2089): 2475.8027944529676, (11, 2090): 2478.1241384564296, (11, 2092): 2474.086368873655, (11, 2098): 2453.8069966496864, (11, 2099): 2457.4482599661333, (11, 2101): 2453.8037491300206, (11, 2102): 2468.239408763003, (11, 2103): 2463.938318421091, (11, 2104): 2461.8628111225485, (11, 2106): 2484.5988699044974, (11, 2112): 2456.269088648049, (11, 2113): 2470.655187341858, (11, 2114): 2475.1497810394453, (11, 2117): 2487.2866226407186, (11, 2123): 2442.3542826748194, (11, 2124): 2445.328984791857, (11, 2134): 2438.465898972929, (11, 2138): 2446.5736265425085, (11, 2141): 2439.0006730649757, (11, 2148): 2449.5886943331748, (11, 2150): 2432.059786473773, (11, 2151): 2435.649574682693, (11, 2152): 2430.8409754639747, (11, 2153): 2450.0002485709197, (11, 2154): 2437.2812389329188, (11, 2155): 2436.9141153964206, (11, 2156): 2433.867151318099, (11, 2157): 2440.8291209458193, (11, 2160): 2453.7421831229653, (11, 2161): 2430.948324435674, (11, 2162): 2452.8759890186116, (11, 2163): 2448.4862415970347, (11, 2164): 2448.58384160118, (11, 2168): 2436.468303231328, (11, 2172): 2442.1057822646494, (11, 2174): 2436.076432923689, (11, 2178): 2445.385186842008, (11, 2179): 2443.695712444724, (11, 2183): 2447.094147168525, (11, 2185): 2447.668225931299, (11, 2186): 2445.0881517142857, (11, 2190): 2453.64281206849, (11, 2192): 2449.130836395641, (11, 2193): 2447.7120152829107, (11, 2194): 2443.1056625795873, (11, 2195): 2443.269249358258, (11, 2197): 2450.524052680241, (11, 2205): 2445.2496806976114, (11, 2207): 2438.1256987355437, (11, 2208): 2442.2752046972473, (11, 2212): 2447.2373005932477, (11, 2214): 2369.191575637019, (11, 2225): 2382.3326781174633, (11, 2231): 2343.4125508658826, (11, 2278): 2432.5578914014086, (11, 2284): 2443.1878555653616, (11, 2285): 2442.419307796036, (11, 2291): 2427.4706190365846, (11, 2292): 2425.2126924461354, (11, 2307): 2437.237200213807, (11, 2313): 2426.6132992951593, (11, 2317): 2416.594642318896, (11, 2319): 2428.8418587448527, (11, 2321): 2433.8296423206425, (11, 2323): 2432.062696210427, (11, 2326): 2446.142654996212, (11, 2327): 2442.0967509340726, (11, 2329): 2439.459402139409, (11, 2330): 2436.738822447869, (11, 2332): 2443.967907099369, (11, 2344): 2431.9202975192497, (11, 2346): 2432.572036237984, (11, 2361): 2423.959815104079, (11, 2368): 2475.2224709482957, (11, 2374): 2480.327678116565, (11, 2375): 2481.400952646517, (11, 2377): 2465.1975658484325, (11, 2378): 2484.5721230595996, (11, 2379): 2485.8071350334235, (11, 2380): 2486.7519775677365, (11, 2383): 2468.847557329879, (11, 2385): 2470.9635627122093, (11, 2395): 2470.4830881191087, (11, 2397): 2484.3298051529473, (11, 2398): 2460.12840409805, (11, 2399): 2465.3693573030855, (11, 2400): 2464.088944265576, (11, 2402): 2475.3830515022087, (11, 2403): 2478.9427337643606, (11, 2404): 2479.51611934377, (11, 2405): 2471.246531637128, (11, 2407): 2477.484932068516, (11, 2408): 2482.018465483683, (11, 2409): 2473.6238271266975, (11, 2411): 2480.3090289843317, (11, 2412): 2478.853347862369, (11, 2413): 2481.964143749124, (11, 2414): 2477.4066154004067, (11, 2422): 2479.710564814065, (11, 2424): 2479.552574614383, (11, 2426): 2480.0402617139316, (11, 2433): 2473.963024960006, (11, 2436): 2473.1134148827828, (11, 2437): 2452.132528276448, (11, 2440): 2456.5079569124696, (11, 2445): 2555.487528366025, (11, 2447): 2543.4703602958807, (11, 2454): 2554.0318213754413, (11, 2455): 2553.9699989523447, (11, 2460): 2522.0393250098214, (11, 2461): 2526.1225680267316, (11, 2471): 2595.049655986485, (11, 2492): 2550.44733740287, (11, 2511): 2513.867331918843, (11, 2523): 2532.6691846839603, (11, 2525): 2529.071777236481, (11, 2535): 2524.7081133106353, (11, 2537): 2517.923891179686, (11, 2538): 2521.986702139765, (11, 2539): 2522.9393814712435, (11, 2540): 2527.863710189836, (11, 2542): 2533.8411537545517, (11, 2559): 2628.5400252699114, (11, 2575): 2623.0299064478104, (11, 2599): 2461.521838461659, (11, 2600): 2497.826317668208, (11, 2607): 2474.47246813829, (11, 2627): 2544.4060622399957, (11, 2647): 2565.339284008695, (11, 2674): 2552.4261535331016, (11, 2681): 2551.341037500697, (11, 2683): 2559.8844516239446, (11, 2686): 2548.5237141057587, (11, 2689): 2673.2106081802003, (11, 2690): 2674.18033939216, (11, 2713): 2709.0437734547027, (11, 2714): 2712.6101797390334, (11, 2715): 2715.566533089405, (11, 2739): 2712.5041444981266, (11, 2740): 2689.672334665101, (11, 2741): 2690.8474500678326, (11, 2749): 2709.990517087913, (11, 2750): 2710.386810896704, (11, 2752): 2712.2562728224484, (11, 2755): 2714.9318224010617, (11, 2758): 2714.6937183993837, (11, 2759): 2714.465939192078, (11, 2769): 2710.4217993606117, (11, 2771): 2695.5436685578493, (11, 2779): 2700.342646601823, (11, 2784): 2668.568714485922, (11, 2800): 2678.354137444761, (11, 2802): 2685.9991506259016, (11, 2803): 2684.3815863095583, (11, 2804): 2682.201765144398, (11, 2805): 2689.972113906033, (11, 2807): 2689.2942168282366, (11, 2809): 2689.2852305419774, (11, 2812): 2668.943413281388, (11, 2814): 2691.5266122617904, (11, 2817): 2696.545661129097, (11, 2819): 2688.4762348493537, (11, 2823): 2675.043849073131, (11, 2832): 2694.3657294045443, (11, 2836): 2680.8896080262175, (11, 2839): 2688.7517929661694, (11, 2841): 2695.0005675457023, (11, 2843): 2693.2202181783364, (11, 2846): 2685.5285732509997, (11, 2849): 2697.295977461929, (11, 2852): 2693.922104394043, (11, 2853): 2698.879043468605, (11, 2876): 2702.5205930308916, (11, 2877): 2713.664263311303, (11, 2885): 2721.5433679019507, (11, 2918): 2686.8399822374627, (11, 2921): 2692.090180686909, (11, 2925): 2665.824163885772, (11, 2926): 2656.1113837528756, (11, 2930): 2680.5701576983697, (11, 2931): 2669.21850863712, (11, 2938): 2687.7627663415587, (11, 2940): 2697.22954077016, (11, 2947): 2680.199638329398, (11, 2949): 2678.476755670729, (11, 2950): 2681.4251881288274, (11, 2952): 2679.146037502563, (11, 2958): 2678.346365251333, (11, 2959): 2679.5812976254724, (11, 2960): 2685.0447508389766, (11, 2961): 2682.9703211282576, (11, 2963): 2676.887527178693, (11, 2968): 2678.8597110191195, (11, 2976): 2675.7575722874544, (11, 2981): 2638.1667981393207, (11, 2982): 2637.9239456975893, (11, 2984): 2635.8929309981145, (11, 3003): 2633.0359252443495, (11, 3046): 2591.74747320671, (11, 3050): 2620.591274609571, (11, 3051): 2621.9936882552306, (11, 3053): 2617.426213890064, (11, 3069): 2647.034807173238, (11, 3071): 2613.8848576061705, (11, 3080): 2723.2696736166727, (11, 3199): 2631.821972249994, (11, 3200): 2627.2628700177133, (11, 3205): 2658.9817291274403, (11, 3209): 2630.1143886536433, (11, 3215): 2627.02808055255, (11, 3217): 2620.7329933701635, (11, 3249): 2627.0125007703546, (11, 3263): 2674.303881298716, (11, 3289): 2640.442751374833, (11, 3301): 2643.4133617408515, (11, 3302): 2640.6077401556713, (11, 3307): 2637.6262539723666, (11, 3310): 2646.1251661029455, (11, 3391): 2679.360371672753, (11, 3509): 1592.7092508049661, (11, 3510): 1588.1600873861557, (11, 3511): 1590.3334896888082, (11, 3512): 1586.768723799803, (11, 3514): 1587.0457811456763, (11, 3519): 1607.5569989776407, (11, 3536): 1599.2304065050216, (11, 3545): 1605.508496605289, (11, 3548): 1597.4109435930848, (11, 3572): 1602.8524351080282, (11, 3581): 1600.1898947074633, (11, 3583): 1593.573832947133, (11, 3601): 1617.4190335263365, (11, 3656): 1613.3030778289535, (11, 3669): 1611.478364522593, (11, 3670): 1615.8517491495522, (11, 3695): 1589.6188975656135, (11, 3696): 1592.7128017903767, (11, 3782): 1584.1996942841179, (11, 3792): 1581.4614391788803, (11, 3989): 729.4539580287246, (11, 4008): 752.9032823890716, (11, 4031): 762.8213489714557, (11, 4045): 743.5777795340956, (11, 4144): 734.1166794232573, (11, 4145): 698.7660492394406, (11, 4164): 722.2614228631704, (11, 4168): 709.4447408324801, (11, 4173): 705.2127885314833, (11, 4181): 690.9293863304002, (11, 4228): 690.0914816545178, (11, 4248): 667.2454699392283, (11, 4254): 486.8776584240841, (11, 4260): 493.4463720472935, (11, 4262): 497.48816987178986, (11, 4273): 499.63956598668, (11, 4319): 391.7682681231542, (11, 4326): 390.79744731594246, (11, 4328): 393.5927802327343, (11, 4334): 393.14499829826735, (11, 4335): 390.1171453971667, (11, 4372): 413.92780809822113, (11, 4413): 481.4873805116871, (11, 4434): 406.87116616011417, (11, 4447): 397.46909687745443, (11, 4452): 409.9792749152028, (11, 4463): 452.3213132912363, (11, 4465): 446.86057225168685, (11, 4619): 534.2131789350179, (11, 4645): 534.0034864223478, (11, 4657): 538.6784297889669, (11, 4666): 541.1743131322693, (11, 4676): 545.9418631146466, (11, 4678): 544.2966466107378, (11, 4689): 547.8883275906989, (11, 4704): 574.9793884699985, (11, 4726): 763.9682970986651, (11, 4727): 760.95423745836, (11, 4730): 754.7682250818744, (11, 4731): 758.806255956637, (11, 4734): 749.2147947282256, (11, 4735): 748.2862029359366, (11, 4736): 751.4102907004843, (11, 4737): 748.630800964029, (11, 4738): 750.6710785160806, (11, 4756): 754.7202410552096, (11, 4760): 730.0960110561132, (11, 4761): 728.0001906064704, (11, 4762): 728.291369586217, (11, 4765): 732.7198714730113, (11, 4773): 768.0254372198484, (11, 4774): 768.4148855616236, (11, 4790): 765.5609150428351, (11, 4795): 762.1568955166623, (11, 4799): 771.3491641398703, (11, 4801): 781.8688538516298, (11, 4804): 759.3394701729434, (11, 4805): 756.5865668827045, (11, 4806): 771.8244438527881, (11, 4815): 771.6701237284173, (11, 4816): 777.7862317858086, (11, 4817): 782.8321539537593, (11, 4826): 777.2587379413753, (11, 4830): 774.5204322646265, (11, 4839): 739.0550262449729, (11, 4840): 743.2697531295631, (11, 4841): 738.1625003331706, (11, 4846): 735.473015167966, (11, 4848): 737.8737060792205, (11, 4850): 741.1316266967364, (11, 4871): 692.099979791973, (11, 4883): 722.222965923492, (11, 4900): 702.3959010526197, (11, 4901): 701.1094811011614, (11, 4917): 601.9969757465498, (11, 4931): 586.9489905945421, (11, 4944): 601.10549707853, (11, 4956): 592.3260308626251, (11, 4958): 597.1359440585416, (11, 4959): 597.9319211978582, (11, 4961): 593.2168078679164, (11, 4966): 591.7422223154153, (11, 5207): 576.1893794418485, (11, 5272): 248.400463817324, (11, 5283): 247.81070138202523, (11, 5287): 259.86367534124594, (11, 5289): 260.49527334349636, (11, 5293): 237.07954967987078, (11, 5295): 233.7805680289468, (11, 5296): 241.21839944205004, (11, 5298): 245.41542755880454, (11, 5303): 251.63620240972216, (11, 5305): 262.87521106079254, (11, 5306): 273.88424419748037, (11, 5307): 264.08486224531896, (11, 5308): 264.75887308620315, (11, 5313): 255.72396270768928, (11, 5314): 252.326304162274, (11, 5317): 269.5157260709939, (11, 5319): 253.757046297423, (11, 5324): 248.30952363344238, (11, 5326): 244.52113810141213, (11, 5348): 280.3271178048172, (11, 5351): 290.0196545797479, (11, 5399): 271.83635065350256, (11, 5413): 306.4224195424579, (11, 5422): 264.09531902760097, (11, 5445): 267.90722003545005, (11, 5448): 268.55639662065295, (11, 5456): 276.6648665694885, (11, 5467): 278.288516368067, (11, 5624): 276.10763521827914, (11, 5671): 167.15397656525093, (11, 5672): 160.78175785407169, (11, 5797): 262.9964267605418, (11, 5871): 374.1310313185541, (11, 5976): 353.68685347407364, (11, 6118): 2203.9997217261202, (11, 6248): 2322.00681794417, (11, 6345): 723.4379074923759, (11, 6352): 745.0257672673056, (11, 6354): 716.3672732425974, (11, 6359): 715.3343066672203, (11, 6376): 749.4071989036323, (11, 6378): 719.2902929243912, (11, 6381): 719.3424723491742, (11, 6383): 726.7311379775695, (11, 6396): 734.6886421440851, (11, 6399): 727.0482451780648, (11, 6408): 741.0730111185077, (11, 6409): 722.5375796474437, (11, 6419): 744.944848913045, (11, 6422): 731.670533003819, (11, 6423): 732.9595720809162, (11, 6424): 708.988642739853, (11, 6439): 710.4374407640781, (11, 6464): 713.837699292121, (11, 6465): 718.857269733362, (11, 6469): 722.2273974913697, (11, 6470): 724.9581750371043, (11, 6472): 709.3261742636716, (11, 6480): 699.5958095699623, (11, 6486): 671.8464946071249, (11, 6497): 680.4296913949645, (11, 6503): 695.7645503269589, (11, 6508): 703.2015200672685, (11, 6509): 694.8888303689342, (11, 6521): 690.5790491506473, (11, 6544): 683.2781462111616, (11, 6552): 713.1980452818159, (11, 6553): 715.6788054911103, (11, 6554): 718.323822772921, (11, 6578): 710.3277384950549, (11, 6582): 703.371633931385, (11, 6601): 707.263258471642, (11, 6609): 695.2713514558305, (11, 6610): 692.520995175816, (11, 6611): 697.1230118917738, (11, 6614): 701.6105917042587, (11, 6615): 699.3136510221902, (11, 6616): 689.791229845989, (11, 6617): 693.3904902918424, (11, 6618): 682.5975736172527, (11, 6619): 702.5486166724213, (11, 6620): 686.543014291939, (11, 6621): 688.2361909949319, (11, 6622): 689.8896461553961, (11, 6623): 698.3687522613005, (11, 6624): 697.111283690802, (11, 6625): 699.2646515825202, (11, 6626): 704.0747615956434, (11, 6627): 704.9842597097139, (11, 6628): 683.7907283587975, (11, 6629): 692.563187351324, (11, 6630): 706.3767763581725, (11, 6632): 694.5646252154929, (11, 6634): 706.8618966887213, (11, 6635): 690.7957043313024, (11, 6636): 688.5540483773133, (11, 6637): 695.4430245845009, (11, 6638): 703.0603571305364, (11, 6639): 702.872236088052, (11, 6640): 704.2776603756963, (11, 6641): 685.8135340125698, (11, 6642): 700.8896476713657, (11, 6643): 706.6180018155385, (11, 6645): 700.7708272317994, (11, 6646): 685.9536167236449, (11, 6647): 701.3595891577726, (11, 6653): 700.4054603026352, (11, 6655): 703.8877504808447, (11, 6658): 705.7961233466053, (11, 6662): 698.756679118106, (11, 6819): 802.2149981930152, (11, 6996): 713.6181403878384, (11, 7059): 680.114028167325, (11, 7187): 669.238351426257, (11, 7304): 782.4622501834862, (11, 7528): 682.8722111741266, (11, 7720): 517.0936848848478, (11, 7793): 503.6278948363002, (11, 7807): 506.6390728503542, (11, 7808): 500.6794889593062, (11, 7831): 656.4002843914684, (11, 7850): 644.5343385308394, (11, 7852): 655.4962242714411, (11, 8012): 550.5622873065417, (11, 8125): 413.2894675997596, (11, 8208): 460.1900242808673, (11, 8392): 585.0501524322481, (11, 8651): 963.808019850466, (11, 9088): 865.6655378005594, (11, 9443): 960.34705098621, (11, 9444): 954.0372195300722, (11, 9828): 1105.9619423376623, (11, 9868): 1129.8904264389068, (11, 10180): 404.0877414954699, (11, 10256): 309.13806253407705, (11, 10276): 363.83951567928557, (11, 10378): 396.3105395185535, (11, 10676): 399.32815439273526, (11, 10714): 458.9581793231667, (11, 10730): 465.1436441121928, (11, 10862): 770.5493007311962, (11, 10881): 765.1267249750166, (11, 10883): 767.9752421270252, (11, 10885): 771.1841069446502, (11, 10891): 772.4544917788071, (11, 10909): 767.5516565483108, (11, 10911): 761.2816239135934, (11, 10913): 764.3122760169587, (11, 10915): 761.5326899892242, (11, 10919): 758.3900812515557, (11, 11037): 864.1821368015309, (11, 11039): 858.2289446428738, (11, 11516): 1083.7891197933143, (11, 11856): 394.38987026117474, (11, 11857): 382.92184989788, (11, 11861): 388.5256467009644, (11, 11881): 398.33618460406603, (11, 11902): 389.6148340541391, (11, 11911): 397.61003306365654, (11, 11914): 394.6051290966273, (11, 11922): 397.6971496853158, (11, 11924): 402.1845972191636, (11, 11926): 400.2031911348344, (11, 11950): 415.4798855991083, (11, 11963): 422.5801650330304, (11, 11983): 433.5928649910455, (11, 11985): 425.496590302982, (11, 12009): 437.7608636623118, (11, 12010): 429.1857481786551, (11, 12018): 431.92108308213045, (11, 12020): 431.2991213824275, (11, 12021): 433.7002212559025, (11, 12024): 438.8210349502577, (11, 12025): 434.2390625039228, (11, 12027): 433.71806899322166, (11, 12031): 428.2503672697238, (11, 12032): 427.73821450016214, (11, 12035): 440.63376549875625, (11, 12041): 418.1304878634095, (11, 12045): 381.1317586740817, (11, 12145): 414.4696674940228, (11, 12275): 763.3127098327093, (11, 12294): 761.703117691893, (11, 12358): 828.5229142128126, (11, 12463): 864.8513142120102, (11, 12465): 865.0454130765816, (11, 12482): 862.1155045137344, (11, 12503): 863.8946536869767, (11, 12506): 866.21351727818, (11, 12549): 846.4042108614277, (11, 12559): 847.5874023796599, (11, 12569): 854.7340076664799, (11, 12572): 856.1726473753101, (11, 12574): 851.5379893046028, (11, 12576): 846.648940701597, (11, 12591): 837.772310949121, (11, 12608): 845.9289722283146, (11, 12696): 817.5971025750235, (11, 12710): 819.7607096872916, (11, 12728): 825.1258699899524, (11, 12766): 643.206753352596, (11, 12771): 610.3181765019967, (11, 12790): 612.3501352922525, (11, 12795): 621.6941586886428, (11, 12797): 606.7831622889609, (11, 12798): 604.2502916318566, (11, 12811): 600.8343390614874, (11, 12830): 608.6952890441859, (11, 12848): 594.1461575383249, (11, 12850): 585.4320181298644, (11, 12852): 604.680159702182, (11, 12854): 605.3228633683793, (11, 12859): 589.8814510611196, (11, 12861): 600.3138308399168, (11, 12865): 606.4127461766766, (11, 12866): 602.5177657710287, (11, 12867): 605.3395626464165, (11, 12874): 604.5261654154286, (11, 12875): 602.4116596338007, (11, 12881): 608.6732814881993, (11, 12883): 607.5505088571039, (11, 12885): 603.085745993912, (11, 12888): 605.1185035394462, (11, 12889): 602.5716320619962, (11, 12892): 606.0252391709311, (11, 12893): 607.9332553731318, (11, 12896): 604.7380630313346, (11, 12906): 617.1548732219779, (11, 13018): 696.3542848416794, (11, 13071): 712.4571216147212, (11, 13131): 656.9073985292516, (11, 13146): 635.9115184376975, (11, 13159): 728.6909025077617, (11, 13193): 653.9522491932016, (11, 13198): 646.7541457354415, (11, 13292): 617.4845489792177, (11, 13296): 583.8827852797173, (11, 13406): 702.4042703942387, (11, 13407): 706.4701939136863, (11, 13417): 734.4671518356314, (11, 13418): 736.3557290806656, (11, 13438): 705.9531533507195, (11, 13442): 695.1568740615945, (11, 13443): 698.138447430046, (11, 13764): 1103.7777342279135, (11, 13766): 1099.2588139113834, (11, 13771): 1111.6712903191947, (11, 13783): 1094.3030740438417, (11, 13784): 1090.8794267681144, (11, 13792): 1132.4002286637788, (11, 13824): 1099.0263008311872, (11, 14017): 1026.1519960530263, (11, 14870): 659.1282300651986, (11, 14997): 692.2966567022354, (11, 15000): 689.2301896206297, (11, 15003): 682.7965697199196, (11, 15006): 685.1233970198077, (11, 15007): 680.8718532626004, (11, 15056): 673.6395144160837, (11, 15063): 675.74676513039, (11, 15069): 674.2779442213834, (11, 15076): 678.3778308807379, (11, 15086): 694.2442872793084, (11, 15087): 694.9089743876104, (11, 15111): 709.4753467247301, (11, 15116): 700.849943748566, (11, 15722): 809.2773263671967, (11, 15998): 836.0362482026848, (11, 16073): 1910.3889440277392, (11, 16939): 2256.029844953092, (11, 16940): 2249.692612754699, (11, 16951): 2259.126307155777, (11, 16963): 2259.1872890953173, (11, 16965): 2265.9223556739335, (11, 16969): 2265.444729410794, (11, 16970): 2261.194109896898, (11, 16971): 2255.04477339472, (11, 16973): 2255.432329176862, (11, 16974): 2269.3961579131314, (11, 16976): 2261.1642627954498, (11, 16978): 2256.390939237712, (11, 16980): 2262.7558121510865, (11, 16982): 2270.182104862661, (11, 17045): 2526.4962164113913, (11, 17048): 2534.9455829575227, (11, 17304): 619.4667587051498, (11, 17305): 624.6348335487855, (11, 17330): 624.9903502705281, (11, 17334): 611.90257190629, (11, 17343): 631.2100467059571, (11, 17345): 620.397009509709, (11, 17347): 630.2283365669268, (11, 17351): 603.7138809362771, (11, 17372): 614.522509659578, (11, 17373): 629.5343168352339, (11, 17377): 631.2973515973457, (11, 17382): 623.3502101110352, (11, 17383): 621.917948940186, (11, 17389): 617.9410071860524, (11, 17400): 624.6052891102003, (11, 17401): 623.0767886901235, (11, 17402): 625.909614090011, (11, 17403): 627.4042182178711, (11, 17440): 630.3451928319482, (11, 17455): 635.5241091032434, (11, 17491): 642.6820803337788, (11, 17507): 587.0902441353498, (11, 17509): 589.0420985353473, (11, 17590): 610.8416068050163, (11, 17615): 531.8952338719251, (11, 17642): 540.3880721695164, (11, 17643): 543.4093828809174, (11, 17668): 529.6123144601867, (11, 17721): 500.96401717513083, (11, 17754): 535.311471714155, (11, 17769): 578.6496786158532, (11, 17776): 578.3269041276243, (11, 17804): 583.8610364727584, (11, 17809): 588.0122554643735, (11, 17824): 579.9411200652802, (11, 17837): 593.5068813980395, (11, 17838): 598.8572359759613, (11, 17862): 598.2573294556829, (11, 17866): 604.4085931133658, (11, 17872): 592.417330391752, (11, 17873): 588.9483797342374, (11, 17881): 595.0459719079764, (11, 17947): 1719.0148102179612, (11, 17951): 1709.2503040509157, (11, 17953): 1706.4324063306021, (11, 17954): 1706.4917866832118, (11, 17959): 1718.6425916869505, (11, 17963): 1716.8583978144372, (11, 18000): 1664.5951974009379, (11, 18001): 1665.267042870187, (11, 18111): 1770.0603308701504, (11, 18148): 1498.2780323835805, (11, 18166): 1597.959828344682, (11, 18189): 1701.8148526356583, (11, 18239): 628.335781677648, (11, 18240): 629.2329599424459, (11, 18245): 629.20584145523, (11, 18247): 629.3226762352692, (11, 18251): 630.341406037346, (11, 18256): 632.5478797260338, (11, 18258): 632.0734162223149, (11, 18259): 632.7671633312835, (11, 18260): 633.8764205918467, (11, 18262): 635.2877912604117, (11, 18263): 633.3544852617335, (11, 18264): 634.3970219299349, (11, 18266): 636.4329551670717, (11, 18267): 637.3195505170926, (11, 18268): 638.1090197546243, (11, 18269): 639.9765127525764, (11, 18275): 639.0997537945807, (11, 18285): 633.6695123645347, (11, 18308): 614.0652258739005, (11, 18313): 610.0874836967639, (11, 18314): 614.8631847081803, (11, 18315): 637.2656230733071, (11, 18316): 638.4086307020935, (11, 18317): 639.3619220727238, (11, 18320): 638.4258705313292, (11, 18321): 639.5211010103324, (11, 18322): 640.7655539978779, (11, 18324): 639.9755567243218, (11, 18325): 642.0918945188932, (11, 18326): 641.2450328072592, (11, 18327): 641.2939645235481, (11, 18329): 641.6353241397386, (11, 18330): 644.5020513095537, (11, 18331): 642.4661271052024, (11, 18332): 641.0224673582688, (11, 18333): 643.158317103484, (11, 18336): 640.0821922075522, (11, 18337): 639.9957624384142, (11, 18403): 646.0296380758743, (11, 18432): 655.2383182079473, (11, 18451): 648.9799482095361, (11, 18466): 640.3179567374677, (11, 18481): 634.4632266213089, (11, 18483): 635.3572072143351, (11, 18484): 633.5056264346327, (11, 18485): 627.0169412176795, (11, 18486): 626.9433580595385, (11, 18487): 623.1326804434399, (11, 18489): 629.6624933623405, (11, 18490): 629.9402503423022, (11, 18491): 631.2205799970993, (11, 18492): 621.1591193113483, (11, 18493): 625.4153351931012, (11, 18494): 629.8719946197727, (11, 18495): 628.8520504783862, (11, 18496): 628.2493128558225, (11, 18497): 621.4208997509926, (11, 18498): 625.715634738876, (11, 18499): 628.0430589710776, (11, 18501): 624.7652640764461, (11, 18502): 623.1714358987949, (11, 18503): 623.0489403663694, (11, 18504): 629.8876496792831, (11, 18506): 622.395922422353, (11, 18507): 620.3605238936055, (11, 18508): 626.8445704778696, (11, 18509): 626.0194013892219, (11, 18510): 621.8239008623499, (11, 18511): 624.0268756154682, (11, 18512): 623.9843712150129, (11, 18515): 628.7498936463068, (11, 18516): 625.9076027065324, (11, 18517): 622.6014965996383, (11, 18518): 627.920724892789, (11, 18519): 630.7259655367632, (11, 18520): 627.4844045863576, (11, 18522): 638.6845948000204, (11, 18523): 638.0039364281391, (11, 18532): 638.5552251370335, (11, 18535): 636.4078029544997, (11, 18537): 635.2187390319942, (11, 18539): 634.9535411558252, (11, 18540): 634.5491968854692, (11, 18541): 634.6874089936205, (11, 18542): 634.8696518514896, (11, 18543): 633.5688132425879, (11, 18546): 632.5158455019258, (11, 18555): 634.3014991562545, (11, 18556): 633.9603686537549, (11, 18565): 637.0969748127869, (11, 18567): 635.7013170909403, (11, 18568): 635.5423037969692, (11, 18577): 643.0768603969408, (11, 18583): 644.4738276789336, (11, 18605): 649.2776664094794, (11, 18608): 632.4314565988499, (11, 18616): 656.2295194039456, (11, 18618): 660.596246680428, (11, 18625): 665.5115589878573, (11, 18645): 663.0789286580774, (11, 18646): 662.1332381525344, (11, 18653): 650.3688126287682, (11, 18654): 654.9253651563076, (11, 18655): 650.4701901104378, (11, 18666): 682.1647112871511, (11, 18837): 765.8802925716943, (11, 18974): 672.0384993822984, (11, 18999): 689.0328793913897, (11, 19000): 690.972375924779, (11, 19174): 684.6647488299915, (11, 19342): 735.6011823641624, (11, 19455): 641.3388119284457, (11, 19555): 626.9912799242247, (11, 19564): 663.0294639359489, (11, 19573): 654.1757880012624, (11, 19586): 648.0411170453856, (11, 19605): 643.2221156226298, (11, 19611): 647.916790293222, (11, 19614): 636.5461690142326, (11, 19641): 677.7423257480954, (11, 19702): 687.3531338437509, (11, 19713): 681.959365108641, (11, 19731): 570.987524247373, (11, 19819): 651.3495743724649, (11, 19893): 87.22189150763927, (11, 19899): 75.80447054962329, (11, 19929): 89.46772852108816, (11, 19951): 112.28776610627851, (11, 19962): 74.54308223708829, (11, 19970): 103.62921229430802, (11, 19971): 97.23997024483239, (11, 19972): 91.97166596077942, (11, 19975): 96.48434925621468, (11, 19978): 139.68890969587997, (11, 19987): 143.3005040534283, (11, 19989): 133.02865712354836, (11, 20039): 146.86122028281866, (11, 20043): 155.79876008530323, (11, 20047): 155.74027882897246, (11, 20052): 141.3328902387608, (11, 20054): 139.82998539329918, (11, 20085): 227.68482316426014, (11, 20104): 233.03066711939368, (11, 20132): 197.76619102984034, (11, 20203): 23.31351193472613, (11, 20280): 3.1974248331626787, (11, 20285): 5.464263941026361, (11, 20290): 7.688300759300216, (11, 20297): 9.885439526786016, (11, 20309): 121.97868209933988, (11, 20453): 229.1274059743938, (11, 20485): 56.30123688898099, (11, 20520): 77.1553471440027, (11, 20526): 73.94408615457203, (11, 20698): 1361.7194017568856, (11, 20868): 1542.2964926392076, (11, 21042): 421.37091707446496, (11, 21057): 414.19247819338295, (11, 21066): 408.49345852420964, (11, 21075): 422.36195174266595, (11, 21093): 408.9266069161063, (11, 21098): 385.2897709402309, (11, 21127): 414.33817975319636, (11, 21130): 406.7755968371117, (11, 21144): 418.2115281805832, (11, 21146): 415.0477818864518, (11, 21147): 421.7152159691377, (11, 21148): 416.281069812676, (11, 21153): 463.65315314794645, (11, 21293): 394.9420481258628, (11, 21426): 509.8919027338476, (11, 21442): 532.9500867758024, (11, 21451): 534.9021249957598, (11, 21466): 514.6180180302543, (11, 21469): 512.4151379961608, (11, 21471): 516.0147796771884, (11, 21473): 512.7561689235048, (11, 21475): 514.1252602604934, (11, 21482): 515.7382069231076, (11, 21484): 513.715168505418, (11, 21488): 516.2423211404915, (11, 21494): 507.68289671839767, (11, 21498): 507.64024717340294, (11, 21500): 502.64200025450526, (11, 21514): 476.8810375230087, (11, 21537): 488.4914897883212, (11, 21662): 459.10503264888655, (11, 21691): 462.98914769325694, (11, 21757): 520.4134292957104, (11, 21777): 417.98238063754053, (11, 21778): 422.0827644368989, (11, 21779): 415.1818431202285, (11, 21790): 418.5702801521286, (11, 21802): 409.55813364364394, (11, 21824): 400.7261864243747, (11, 21874): 408.49669352339583, (11, 21879): 402.7889682227008, (11, 21983): 434.2856954814327, (11, 22002): 364.6247540857738, (11, 22132): 509.4863872731438, (11, 22261): 1122.4028596993128, (11, 22298): 1106.0459445221811, (11, 22339): 1177.426749222235, (11, 22508): 993.6776986062644, (11, 22841): 2707.005257271736, (11, 22842): 2706.708838388005, (11, 22874): 2689.233433943014, (11, 22941): 2692.034996859337, (11, 22956): 2701.730563892129, (11, 22960): 2705.46515228085, (11, 22968): 2710.69648100799, (11, 22970): 2714.1130716439543, (11, 22974): 2716.0261993148238, (11, 22980): 2727.974085648771, (11, 23025): 2722.271210455291, (11, 23028): 2718.6509069943363, (11, 23081): 2732.875241415852, (11, 23104): 2702.8673164186307, (11, 23147): 2611.191720510396, (11, 23298): 444.1781230979526, (11, 23376): 439.2360032639015, (11, 23381): 407.4975180816513, (11, 23529): 423.84401843217404, (11, 23556): 424.33332680599074, (11, 23718): 465.2643149973056, (11, 24001): 494.8607295591579, (11, 24094): 466.5921138200065, (11, 24129): 477.7909374732513, (11, 24174): 436.40134342510737, (11, 24235): 449.0319042513568, (11, 24259): 472.41637273996184, (11, 24260): 469.7416163820565, (11, 24261): 468.85233875918897, (11, 24305): 491.4862660366818, (11, 24306): 491.5814498488345, (11, 24307): 489.2610210322799, (11, 24308): 550.9326913445775, (11, 24498): 558.6415740172806, (11, 24499): 558.1127160580787, (11, 24500): 556.5714029555404, (11, 24668): 585.0452196536132, (11, 24711): 556.9341189141508, (11, 24756): 551.6721583085125, (11, 24788): 561.7325164448838, (11, 24809): 531.7949221302384, (11, 24813): 542.3498283452163, (11, 24821): 539.4371694148208, (11, 24825): 539.2037495041079, (11, 24832): 531.6854247926718, (11, 24833): 534.8681836567424, (11, 24835): 537.3203202686724, (11, 24837): 544.0992284644419, (11, 24840): 530.316269437423, (11, 24841): 537.0479832454023, (11, 24844): 529.2744132699471, (11, 24845): 536.8070465092175, (11, 24846): 530.0181276529552, (11, 24849): 531.193054856547, (11, 24850): 541.8828321523713, (11, 24863): 506.9082183497103, (11, 24866): 512.8811125114739, (11, 24885): 515.4105430753077, (11, 24886): 513.2680514001968, (11, 24889): 534.968320026474, (11, 24903): 543.8463906139366, (11, 24909): 529.8924698853556, (11, 24999): 809.963731056285, (11, 25019): 811.6322186799783, (11, 25028): 804.4622278901011, (11, 25137): 90.40958532860657, (11, 25145): 90.33321621672205, (11, 25208): 184.15011192687476, (11, 25233): 182.117732067792, (11, 25371): 39.660156712489474, (11, 25377): 25.275467445796455, (11, 25828): 390.9755819142578, (11, 25851): 448.2965483874974, (11, 25874): 392.9558295009599, (11, 25898): 369.74003333027827, (11, 25946): 396.780871868918, (11, 26047): 288.12113419046744, (11, 26066): 158.34572654805692, (11, 26197): 225.47811607645173, (11, 26212): 594.7081838984882, (11, 26253): 615.7747092818458, (11, 26254): 607.3688125086686, (11, 26257): 601.1940876110917, (11, 26258): 611.8906571356421, (11, 26260): 606.2982486465218, (11, 26266): 611.7850685289558, (11, 26267): 605.5446061180858, (11, 26271): 605.608045081899, (11, 26304): 531.7743997349605, (11, 26305): 532.0801200879438, (11, 26363): 414.550125402349, (11, 26441): 1097.9940172299605, (11, 26442): 1096.803175037859, (11, 26450): 1085.913240463685, (11, 26459): 1080.8840060194188, (11, 26462): 1080.571332839306, (11, 26467): 1111.8668544947811, (11, 26471): 1105.1652328372327, (11, 26472): 1104.846120420097, (11, 26473): 1105.0767999455554, (11, 26476): 1106.2293646699145, (11, 26485): 1088.2626173409944, (11, 26493): 1090.7430214161914, (11, 26524): 1083.4269945845406, (11, 26525): 1083.3241620274814, (11, 26556): 1100.7351286865335, (11, 26560): 1096.2736569934023, (11, 26561): 1088.7112763218684, (11, 26564): 1098.7908539497384, (11, 26569): 1088.192533567008, (11, 26570): 1086.8115231924019, (11, 26573): 1090.3853416995883, (11, 26581): 1091.803261086144, (11, 26583): 1088.4354566658972, (11, 26593): 1093.9968791443087, (11, 26837): 1115.658554904939, (11, 26844): 1122.0447141724796, (11, 26863): 1112.2199781540319, (11, 26893): 1132.2008139013221, (11, 26902): 1141.0061402401095, (11, 26905): 1128.4895124314594, (11, 26912): 1136.5129731955194, (11, 26921): 1121.5351341781993, (11, 26922): 1109.8805775043043, (11, 27212): 1090.3087317560294, (11, 27218): 1079.0988442625937, (11, 27239): 1104.4710538784827, (11, 27257): 1098.3418071813237, (11, 27274): 1107.7618028174563, (11, 27279): 1107.2824724036116, (11, 27282): 1099.2230467298875, (11, 27283): 1100.4003255311736, (11, 27285): 1112.029749149764, (11, 27286): 1106.4504478684964, (11, 27290): 1092.5083715334729, (11, 27295): 1085.991816332217, (11, 27300): 1108.7479655288437, (11, 27344): 1091.8952762761649, (11, 27366): 1102.0317244880794, (11, 27383): 1114.8992304939652, (11, 27398): 1122.2254999402378, (11, 27406): 1113.454201259455, (11, 27407): 1115.0221740631666, (11, 27426): 1097.6294223498737, (11, 27432): 1064.7519704852978, (11, 27460): 1084.4069482831728, (11, 27523): 1121.8574830746202, (11, 27545): 1245.9155839091284, (11, 27602): 1438.1084408089785, (11, 27606): 1440.397026635416, (11, 27646): 1265.1233665480368, (11, 27667): 1302.6879877045271, (11, 27672): 1303.857936915464, (11, 27674): 1297.9471792782583, (11, 27688): 1300.1706368567882, (11, 27692): 1311.2780750825725, (11, 27693): 1305.817258851129, (11, 27705): 1306.436406387654, (11, 27712): 1309.8937500036552, (11, 27786): 1418.9396001803773, (11, 27790): 1388.5668162915179, (11, 27791): 1385.484743025471, (11, 27795): 1409.1042910044494, (11, 27801): 1387.2458310138395, (11, 27813): 1425.8274118939212, (11, 27816): 1417.091566804933, (11, 27823): 1386.3379913932133, (11, 27830): 1406.6223597671185, (11, 27884): 1212.4573247452868, (11, 27885): 1250.8272969079155, (11, 27896): 1227.0475125061773, (11, 27919): 1224.5021575538667, (11, 27922): 1230.650843569705, (11, 27930): 1217.04343679782, (11, 27934): 1219.3447573938488, (11, 27935): 1221.3843728773827, (11, 27948): 1458.1638863351425, (11, 27951): 1455.1324729402747, (11, 28061): 1399.9527910806728, (11, 28290): 1751.852400508684, (11, 28292): 1762.7882787776073, (11, 28293): 1754.2459643416353, (11, 28295): 1753.1398376283069, (11, 28296): 1752.5861836706274, (11, 28297): 1746.2725061320086, (11, 28302): 1745.4606205768935, (11, 28310): 2034.9847579770862, (11, 28313): 2044.6046007897805, (11, 28372): 2038.756644492921, (11, 28398): 2039.901777947793, (11, 28399): 2037.8022104244944, (11, 28400): 2042.1166253291326, (11, 28401): 2029.9161013241699, (11, 28445): 2042.8935150761379, (11, 28475): 2016.3215083953162, (11, 28885): 377.99635212157455, (11, 28886): 372.83833392296077, (11, 28915): 362.8703432788476, (11, 28916): 364.7820094264899, (11, 28917): 361.00661028131105, (11, 28921): 384.71293328734663, (11, 28931): 380.96421195388314, (11, 28945): 329.8779962686723, (11, 28982): 345.8538774576507, (11, 29219): 297.2264267067807, (11, 29228): 288.9769041601694, (11, 29246): 328.5211787101078, (11, 29248): 318.8784316415633, (11, 29282): 305.4132287510589, (11, 29290): 345.0638980905015, (11, 29291): 339.56427881654747, (11, 29292): 343.46091619758045, (11, 29293): 337.8420750300239, (11, 29294): 338.61670520561154, (11, 29298): 335.92510480718516, (11, 29299): 333.0869917465292, (11, 29304): 333.19622380108717, (11, 29317): 323.9507546998879, (11, 29323): 323.5766897647409, (11, 29330): 327.39214354805233, (11, 29331): 331.4890304411489, (11, 29344): 275.97047126180706, (11, 29445): 167.9636087751525, (11, 29724): 2688.3224683658623, (11, 29738): 2691.497079011786, (11, 29745): 2682.534386627207, (11, 29748): 2685.860289521707, (11, 29750): 2691.6724613428596, (11, 29759): 2681.3234208223807, (11, 29772): 2693.087445468493, (11, 29781): 2690.561746939013, (11, 29784): 2687.9080011264628, (11, 29790): 2693.383825786685, (11, 29811): 2687.3387249806215, (11, 29817): 2712.7972602435766, (11, 29818): 2710.356991681582, (11, 29929): 2680.4737371889128, (11, 30039): 2717.381086467181, (11, 30066): 2687.9500766639044, (11, 30116): 2583.6042307813345, (11, 30238): 2428.11359429489, (11, 30248): 2500.0568988361147, (11, 30260): 2501.367280027663, (11, 30545): 393.91543882845866, (11, 30733): 397.2874707804455, (11, 30756): 334.6688025701661, (11, 30921): 351.576940337565, (11, 31079): 819.9094408908854, (11, 31149): 778.8390821018658, (11, 31154): 786.6712385309951, (11, 31160): 778.2203832259034, (11, 31163): 787.468818740977, (11, 31189): 795.772301615805, (11, 31215): 802.0004935913998, (11, 31259): 839.0746990470118, (11, 31262): 838.3218984600489, (11, 31430): 843.3598134879862, (11, 31568): 956.7087372929326, (11, 31751): 846.1769585319528, (13, 109): 674.3564113556318, (13, 872): 1706.9763034843597, (13, 873): 1714.7923472504071, (13, 877): 1711.376235784005, (13, 879): 1712.4892766829194, (13, 884): 1703.5565175655124, (13, 889): 1708.6869785050083, (13, 891): 1701.0969150765277, (13, 892): 1718.6513270358853, (13, 894): 1717.8609160691358, (13, 896): 1711.1349963282635, (13, 903): 1711.1205970441465, (13, 909): 1699.406656638746, (13, 910): 1702.9915279098905, (13, 912): 1697.7186561318254, (13, 913): 1691.7401176684732, (13, 916): 1689.8843392504805, (13, 926): 1706.1566619744215, (13, 927): 1703.638045283087, (13, 948): 1698.339612104231, (13, 961): 1704.8055848147376, (13, 962): 1706.010553065377, (13, 963): 1707.2627370996374, (13, 967): 1714.6226338387655, (13, 974): 1709.309951333532, (13, 998): 1717.3255317393935, (13, 1014): 1894.256470114225, (13, 1086): 1701.7852929280714, (13, 1087): 1702.6137977096346, (13, 1089): 1694.4839360438718, (13, 1090): 1697.6156948537414, (13, 1092): 1708.8319842343658, (13, 1097): 1699.9202642435766, (13, 1107): 1715.5562075660089, (13, 1387): 632.5159723891798, (13, 1554): 530.6039520416458, (13, 1827): 2057.7897711064384, (13, 1828): 2058.8148896908965, (13, 1829): 2059.911019268063, (13, 1830): 2057.8054732145843, (13, 1831): 2058.6688548101542, (13, 1832): 2057.894549916987, (13, 1833): 2058.135664798677, (13, 1836): 2057.3827940686924, (13, 1841): 2062.2638634409795, (13, 1843): 2060.1292810970685, (13, 1844): 2060.9360274198134, (13, 1845): 2058.268248594804, (13, 1847): 2050.4683102576573, (13, 1848): 2053.2478518391154, (13, 1849): 2066.1372734584347, (13, 1850): 2067.6355573558335, (13, 1851): 2054.9899113798024, (13, 1852): 2054.8622292803943, (13, 1854): 2056.45699851009, (13, 1856): 2049.6291216609625, (13, 1857): 2052.8749705103055, (13, 1858): 2065.1002014201567, (13, 1861): 2059.4459132555767, (13, 1866): 2049.162810544791, (13, 1867): 2062.6931015536825, (13, 1868): 2061.254104579667, (13, 1870): 2060.272619552813, (13, 1871): 2062.588347694056, (13, 1875): 2056.5403685372503, (13, 1880): 2051.675605558932, (13, 1882): 2052.0240273351264, (13, 1883): 2068.1225580874966, (13, 1889): 2053.6995476687953, (13, 1893): 2060.6151743878163, (13, 1894): 2058.717956215686, (13, 1899): 2052.1725560553746, (13, 1900): 2053.7570203016935, (13, 1902): 2064.0744992988775, (13, 1905): 2066.4262587104204, (13, 1907): 2055.5024838923973, (13, 1910): 2056.866881903058, (13, 1917): 2072.9411784220897, (13, 1920): 2055.9918674013643, (13, 1935): 2067.42582449696, (13, 1937): 2069.5065617654477, (13, 1946): 2048.5090190985634, (13, 1949): 2051.1446458697264, (13, 1950): 2041.6401994473658, (13, 1951): 2046.0398657413339, (13, 1952): 2048.3010140449665, (13, 1953): 2050.45898767423, (13, 1954): 2047.9045486583464, (13, 1958): 2050.0789695125372, (13, 1960): 2054.0511920016966, (13, 1968): 2055.6212705839657, (13, 1969): 2068.584615954096, (13, 1974): 2065.1354841277907, (13, 1975): 2064.8850261859093, (13, 1979): 2059.333323937236, (13, 1980): 2058.2164376849073, (13, 1981): 2060.370810766211, (13, 1985): 2061.9908091042257, (13, 1994): 2036.7888644116208, (13, 2011): 2051.702891234959, (13, 2019): 2071.6975410402615, (13, 2020): 2069.0466131006096, (13, 2029): 2058.3837928541825, (13, 2030): 2067.219232011923, (13, 2032): 2056.330630860118, (13, 2033): 2062.2975136815076, (13, 2034): 2061.8973012097845, (13, 2036): 2050.0927378985743, (13, 2037): 2053.1604758300964, (13, 2038): 2055.486650017864, (13, 2042): 2087.0194234219066, (13, 2050): 2061.3207157428374, (13, 2051): 2060.5370891619687, (13, 2053): 2061.518017755197, (13, 2054): 2064.296046226077, (13, 2066): 2058.5850963484822, (13, 2067): 2058.7717914163263, (13, 2071): 2031.6959705527454, (13, 2072): 2037.1844915001395, (13, 2073): 2023.6618321682702, (13, 2074): 2022.7370284728868, (13, 2080): 2013.3414239706865, (13, 2082): 2040.0696685385283, (13, 2083): 2042.927912483262, (13, 2089): 2037.3922512886363, (13, 2090): 2040.1151163682932, (13, 2092): 2036.8370448761934, (13, 2098): 2017.1621572103872, (13, 2099): 2020.028286338009, (13, 2101): 2016.3195028561772, (13, 2102): 2031.0537605324278, (13, 2103): 2026.3035945700221, (13, 2104): 2023.5698936287174, (13, 2106): 2044.6398295284273, (13, 2112): 2018.0100223056522, (13, 2113): 2032.9739779321253, (13, 2114): 2036.0300786976773, (13, 2117): 2046.5987433181162, (13, 2123): 2037.1537513716937, (13, 2124): 2040.1900370069636, (13, 2134): 2030.7087154244448, (13, 2138): 2039.9737982430822, (13, 2141): 2032.0154404087195, (13, 2148): 2033.3012280774492, (13, 2150): 2024.4722790917406, (13, 2151): 2027.432829010455, (13, 2152): 2022.5753651543846, (13, 2153): 2034.6227289836806, (13, 2154): 2022.2373984504634, (13, 2155): 2020.2623531098952, (13, 2156): 2018.2983893837925, (13, 2157): 2019.5860805293078, (13, 2160): 2042.6870493506303, (13, 2161): 2021.7346533995653, (13, 2162): 2033.97901921396, (13, 2163): 2029.8166372301282, (13, 2164): 2029.344183412382, (13, 2168): 2024.0697992441642, (13, 2172): 2025.4726572739187, (13, 2174): 2026.6643925286405, (13, 2178): 2027.5481434400301, (13, 2179): 2025.467425760722, (13, 2183): 2039.3963086882663, (13, 2185): 2039.3906256072653, (13, 2186): 2037.0714387720573, (13, 2190): 2043.6270692362011, (13, 2192): 2039.3819218812216, (13, 2193): 2040.3577973991537, (13, 2194): 2036.0219573878687, (13, 2195): 2034.9718911562318, (13, 2197): 2040.106886313967, (13, 2205): 2033.447091815357, (13, 2207): 2024.9130906806224, (13, 2208): 2029.6033049762966, (13, 2212): 2042.5555382954062, (13, 2214): 1947.4853092018516, (13, 2225): 1956.8441063839784, (13, 2231): 1945.2134372581934, (13, 2278): 1997.9087778516625, (13, 2284): 2006.2961217122477, (13, 2285): 2004.7795027341992, (13, 2291): 1985.175094799413, (13, 2292): 1989.1749410451125, (13, 2307): 2000.382011514726, (13, 2313): 1982.4262803499282, (13, 2317): 1983.3597736903323, (13, 2319): 1992.072910441848, (13, 2321): 1995.8717987248954, (13, 2323): 1995.908511564894, (13, 2326): 2012.7612750815185, (13, 2327): 2008.8626824495266, (13, 2329): 2006.140740758928, (13, 2330): 2002.9004681928686, (13, 2332): 2009.0472434714998, (13, 2344): 1999.9569686923555, (13, 2346): 1999.3598853381345, (13, 2361): 2001.3806424079044, (13, 2368): 2044.7873658567096, (13, 2374): 2048.757430473072, (13, 2375): 2050.3987424810944, (13, 2377): 2035.7409065549316, (13, 2378): 2052.921918478365, (13, 2379): 2052.884326340634, (13, 2380): 2054.6552809176465, (13, 2383): 2039.9855910806589, (13, 2385): 2042.440737826337, (13, 2395): 2043.072193529614, (13, 2397): 2050.9196301552556, (13, 2398): 2031.0262707507507, (13, 2399): 2036.5924393431067, (13, 2400): 2035.396807977412, (13, 2402): 2042.7538072050054, (13, 2403): 2046.0618646509822, (13, 2404): 2047.0846742268516, (13, 2405): 2038.9593415641175, (13, 2407): 2045.8264887187977, (13, 2408): 2049.5312824519724, (13, 2409): 2041.4892419436203, (13, 2411): 2045.3472860668953, (13, 2412): 2044.7373077849163, (13, 2413): 2047.3576359743033, (13, 2414): 2042.8496821876709, (13, 2422): 2044.0993747037805, (13, 2424): 2045.8230927704367, (13, 2426): 2046.6809781677773, (13, 2433): 2040.235939438513, (13, 2436): 2038.1397240478982, (13, 2437): 2018.921133774181, (13, 2440): 2023.280217054687, (13, 2445): 2105.390957623523, (13, 2447): 2095.1998425148477, (13, 2454): 2105.1549174250636, (13, 2455): 2106.0255202516605, (13, 2460): 2074.6942682436907, (13, 2461): 2078.490795643001, (13, 2471): 2138.5059283853243, (13, 2492): 2061.376460594731, (13, 2511): 2032.0132253165543, (13, 2523): 2046.9753203119599, (13, 2525): 2041.6709171263824, (13, 2535): 2055.890366509476, (13, 2537): 2048.8105044367494, (13, 2538): 2054.010999989789, (13, 2539): 2050.4507466765485, (13, 2540): 2059.0626553280695, (13, 2542): 2063.6474453999463, (13, 2559): 2165.314458217789, (13, 2575): 2154.5548368935088, (13, 2599): 2010.1870960628844, (13, 2600): 2042.361168259208, (13, 2607): 2025.073475926752, (13, 2627): 2046.2522109465233, (13, 2647): 2063.6561635315475, (13, 2674): 2055.7069055517536, (13, 2681): 2052.4442731049953, (13, 2683): 2061.705179681722, (13, 2686): 2051.790082385815, (13, 2689): 2170.4692996393746, (13, 2690): 2170.8866010916995, (13, 2713): 2189.480199627433, (13, 2714): 2190.930322792999, (13, 2715): 2193.9046917437636, (13, 2739): 2191.431378394497, (13, 2740): 2174.274862094462, (13, 2741): 2175.869969288631, (13, 2749): 2186.739867051909, (13, 2750): 2187.8651528043924, (13, 2752): 2190.075013665929, (13, 2755): 2192.3024493186563, (13, 2758): 2191.451937470989, (13, 2759): 2191.5498415857264, (13, 2769): 2188.3194214143746, (13, 2771): 2178.649268831793, (13, 2779): 2178.1129607375756, (13, 2784): 2144.0500589884136, (13, 2800): 2148.6815752835882, (13, 2802): 2167.72524924447, (13, 2803): 2166.779789373734, (13, 2804): 2164.8685702773682, (13, 2805): 2169.6771596663684, (13, 2807): 2169.675015468285, (13, 2809): 2168.161816426074, (13, 2812): 2149.5642507367475, (13, 2814): 2165.9824716043163, (13, 2817): 2165.1237730925995, (13, 2819): 2170.5154309550644, (13, 2823): 2149.8611436207557, (13, 2832): 2173.110578898953, (13, 2836): 2159.7592964149903, (13, 2839): 2169.8191637770974, (13, 2841): 2166.5408738224532, (13, 2843): 2165.82028688253, (13, 2846): 2161.670548746811, (13, 2849): 2174.8901592704433, (13, 2852): 2171.97263503369, (13, 2853): 2176.2222639807383, (13, 2876): 2176.7518660425026, (13, 2877): 2187.3480955523382, (13, 2885): 2189.0001785563345, (13, 2918): 2173.2356696713027, (13, 2921): 2177.612867109967, (13, 2925): 2157.715268669969, (13, 2926): 2151.4607870028194, (13, 2930): 2164.6335103144443, (13, 2931): 2159.164691021617, (13, 2938): 2172.964985608715, (13, 2940): 2187.9014717910945, (13, 2947): 2172.6179988737676, (13, 2949): 2165.2391385857536, (13, 2950): 2166.9844144620934, (13, 2952): 2164.703532343784, (13, 2958): 2164.393631757506, (13, 2959): 2166.9589403812433, (13, 2960): 2171.891637252971, (13, 2961): 2169.3142933299528, (13, 2963): 2162.2826251810793, (13, 2968): 2163.537549739946, (13, 2976): 2161.874120918232, (13, 2981): 2116.3608076872924, (13, 2982): 2114.7535772747337, (13, 2984): 2112.418185605561, (13, 3003): 2108.0683656816977, (13, 3046): 2082.864252542376, (13, 3050): 2103.9291641076247, (13, 3051): 2105.853761824145, (13, 3053): 2100.725449234421, (13, 3069): 2127.898464836399, (13, 3071): 2100.3929492594216, (13, 3080): 2188.5260542002466, (13, 3199): 2098.667550044452, (13, 3200): 2093.191261692126, (13, 3205): 2125.813393828061, (13, 3209): 2095.90618035814, (13, 3215): 2093.68876148612, (13, 3217): 2087.161083070777, (13, 3249): 2094.4645777980286, (13, 3263): 2143.8339324728818, (13, 3289): 2110.529908550953, (13, 3301): 2111.643089240763, (13, 3302): 2109.457093830858, (13, 3307): 2106.57417764612, (13, 3310): 2114.45265071422, (13, 3391): 2113.4429980774157, (13, 3509): 1075.5544707272481, (13, 3510): 1070.9673147242947, (13, 3511): 1074.4504131941853, (13, 3512): 1071.9925378656287, (13, 3514): 1073.3018199705778, (13, 3519): 1084.30288371559, (13, 3536): 1084.400167106531, (13, 3545): 1092.0334897421114, (13, 3548): 1085.5731800921264, (13, 3572): 1086.4859285262528, (13, 3581): 1079.5317855996095, (13, 3583): 1078.1393277636112, (13, 3601): 1092.3201402628993, (13, 3656): 1083.3890860734625, (13, 3669): 1071.4311732998717, (13, 3670): 1075.443806020293, (13, 3695): 1053.053602811382, (13, 3696): 1056.3663810065118, (13, 3782): 1095.4872154245097, (13, 3792): 1089.1276584478087, (13, 3989): 891.7409613707863, (13, 4008): 915.5242859781914, (13, 4031): 911.586683404331, (13, 4045): 905.4105916103629, (13, 4144): 909.1328042252143, (13, 4145): 888.3346930622732, (13, 4164): 900.64646329389, (13, 4168): 894.6341418423141, (13, 4173): 893.8275812943125, (13, 4181): 879.5004945623924, (13, 4228): 862.7676924483667, (13, 4248): 861.3381369595077, (13, 4254): 755.6644741791931, (13, 4260): 753.7772400877664, (13, 4262): 762.9680835082688, (13, 4273): 759.8243630020847, (13, 4319): 702.3265332393227, (13, 4326): 699.4400236328767, (13, 4328): 699.5496997697556, (13, 4334): 705.9732438221462, (13, 4335): 704.8708952886976, (13, 4372): 1028.5995879238524, (13, 4413): 1111.883553120853, (13, 4434): 1022.3177275485634, (13, 4447): 1021.8025100140708, (13, 4452): 1024.8954640510046, (13, 4463): 953.6207789744271, (13, 4465): 953.6635678178201, (13, 4619): 1150.7631435045705, (13, 4645): 1158.7736414152048, (13, 4657): 1160.5679598664765, (13, 4666): 1159.0360160995249, (13, 4676): 1167.8339849078866, (13, 4678): 1168.0057005169097, (13, 4689): 1166.5172149376344, (13, 4704): 1211.400085003807, (13, 4726): 1397.6821072010873, (13, 4727): 1394.5856472231037, (13, 4730): 1388.351083921663, (13, 4731): 1391.6471071894305, (13, 4734): 1386.4367258773489, (13, 4735): 1384.7932213849585, (13, 4736): 1387.3958848034224, (13, 4737): 1383.7170338203236, (13, 4738): 1385.320791657457, (13, 4756): 1389.107514780784, (13, 4760): 1367.2419478634354, (13, 4761): 1366.4631917527806, (13, 4762): 1364.545508640758, (13, 4765): 1369.5252045112386, (13, 4773): 1402.523209956076, (13, 4774): 1401.789346058521, (13, 4790): 1400.1633011523643, (13, 4795): 1396.9527327973647, (13, 4799): 1404.2009774020357, (13, 4801): 1413.4530294385588, (13, 4804): 1395.4727286858385, (13, 4805): 1392.8645186756987, (13, 4806): 1403.607842977334, (13, 4815): 1402.4334559415556, (13, 4816): 1409.25323619549, (13, 4817): 1413.1228435310327, (13, 4826): 1407.7929348390815, (13, 4830): 1404.4019581947734, (13, 4839): 1376.3772606873486, (13, 4840): 1380.1435351819941, (13, 4841): 1374.4402086232458, (13, 4846): 1371.8988444140964, (13, 4848): 1373.2235729228798, (13, 4850): 1376.380013335405, (13, 4871): 1331.1917644946063, (13, 4883): 1360.8079615358492, (13, 4900): 1342.73369291205, (13, 4901): 1340.4985443766357, (13, 4917): 1191.9935605860765, (13, 4931): 1172.4300440546049, (13, 4944): 1192.6033565675425, (13, 4956): 1177.6337421246324, (13, 4958): 1180.2798323666002, (13, 4959): 1178.785366197581, (13, 4961): 1180.2824638266738, (13, 4966): 1174.7255070478643, (13, 5207): 1153.4920872695373, (13, 5272): 667.2494756708878, (13, 5283): 675.6329660810464, (13, 5287): 697.9686371887395, (13, 5289): 701.9626325858382, (13, 5293): 659.9613722028387, (13, 5295): 682.2618326449349, (13, 5296): 687.5011185108622, (13, 5298): 690.2619556783379, (13, 5303): 701.4528662647115, (13, 5305): 673.4837155684801, (13, 5306): 675.3689922635571, (13, 5307): 669.8687189287294, (13, 5308): 678.940562449073, (13, 5313): 671.5534789600969, (13, 5314): 674.4548570811303, (13, 5317): 682.6573411492769, (13, 5319): 695.1536258653875, (13, 5324): 686.5037665548952, (13, 5326): 680.61563670322, (13, 5348): 678.4565120443882, (13, 5351): 692.2457470173387, (13, 5399): 714.4508284722673, (13, 5413): 714.821609624169, (13, 5422): 713.2272375643907, (13, 5445): 697.8020276978945, (13, 5448): 690.4645435679281, (13, 5456): 694.6853805514887, (13, 5467): 703.0544340217293, (13, 5624): 603.3055445683686, (13, 5671): 779.2155446626002, (13, 5672): 768.0016139873446, (13, 5797): 908.7927851680272, (13, 5871): 868.0765767224274, (13, 5976): 786.3089799295133, (13, 6118): 1619.0998481853694, (13, 6248): 1718.6447488481838, (13, 6345): 28.033142478957632, (13, 6352): 51.051700985123134, (13, 6354): 20.96984993406868, (13, 6359): 19.701197367993558, (13, 6376): 53.875908346373926, (13, 6378): 23.975996069257494, (13, 6381): 23.83100870563077, (13, 6383): 31.86427951425634, (13, 6396): 41.477302267858114, (13, 6399): 31.358688120311978, (13, 6408): 48.09298764699684, (13, 6409): 33.47123254504586, (13, 6419): 68.38109915210131, (13, 6422): 41.79502522731484, (13, 6423): 43.51213131328836, (13, 6424): 19.177544564930322, (13, 6439): 23.503494941936307, (13, 6464): 29.665975892407303, (13, 6465): 31.590743496044485, (13, 6469): 30.121785219067277, (13, 6470): 32.195901013155485, (13, 6472): 14.859449789246764, (13, 6480): 10.722467331222182, (13, 6486): 30.837852746118447, (13, 6497): 22.86620539914506, (13, 6503): 40.06546138841614, (13, 6508): 30.99528304530262, (13, 6509): 32.56859646703743, (13, 6521): 16.001438209551004, (13, 6544): 27.69023759937571, (13, 6552): 38.869222290018634, (13, 6553): 42.08033223463527, (13, 6554): 45.327189569152104, (13, 6578): 32.93923115755303, (13, 6582): 41.06471541031693, (13, 6601): 32.54198305715111, (13, 6609): 3.801934335170368, (13, 6610): 6.014880366578565, (13, 6611): 1.462733417594996, (13, 6614): 6.301886526879047, (13, 6615): 3.7155693015631797, (13, 6616): 6.8458907683679575, (13, 6617): 3.141934602493274, (13, 6618): 14.269454543596684, (13, 6619): 6.867846341570376, (13, 6620): 11.253927464276591, (13, 6621): 11.658517614555231, (13, 6622): 8.624276090511096, (13, 6623): 3.01739775535311, (13, 6624): 6.359679357503513, (13, 6625): 6.032382361803575, (13, 6626): 8.43223577046842, (13, 6627): 10.281832572036976, (13, 6628): 15.625212318830734, (13, 6629): 10.033799784661209, (13, 6630): 10.78354482806751, (13, 6632): 8.060438120246639, (13, 6634): 12.365450211663283, (13, 6635): 9.29810822571198, (13, 6636): 8.412803239060826, (13, 6637): 12.293276959317962, (13, 6638): 8.457221405997789, (13, 6639): 7.7073959666490595, (13, 6640): 8.88963838760941, (13, 6641): 15.137933124253033, (13, 6642): 8.061786268769525, (13, 6643): 11.298362256059153, (13, 6645): 5.29826802758082, (13, 6646): 10.466933565253072, (13, 6647): 7.231822575255148, (13, 6653): 5.00843382149451, (13, 6655): 9.039899344879727, (13, 6658): 12.087647189537385, (13, 6662): 9.014599439349917, (13, 6819): 177.57456408509123, (13, 6996): 162.48615759677617, (13, 7059): 139.58955796700562, (13, 7187): 297.0658913220093, (13, 7304): 280.5870426548383, (13, 7528): 213.73052283052277, (13, 7720): 180.18678844196998, (13, 7793): 197.94622077027557, (13, 7807): 192.9928705672709, (13, 7808): 202.24148139595803, (13, 7831): 41.203045864938446, (13, 7850): 58.38499513548111, (13, 7852): 48.28246471178266, (13, 8012): 145.19592653543887, (13, 8125): 312.0908016911886, (13, 8208): 237.14717095821106, (13, 8392): 120.01309468273529, (13, 8651): 360.4595284313874, (13, 9088): 192.9650495998543, (13, 9443): 511.52705863934875, (13, 9444): 508.5542391079667, (13, 9828): 701.880455110817, (13, 9868): 667.8253262344366, (13, 10180): 324.39600899623423, (13, 10256): 394.822780723828, (13, 10276): 343.39179363859165, (13, 10378): 299.59827957754214, (13, 10676): 403.09711974054005, (13, 10714): 408.7049523081047, (13, 10730): 338.0849459761051, (13, 10862): 983.3415859589736, (13, 10881): 989.7734042717844, (13, 10883): 991.2073434807024, (13, 10885): 981.4356744183854, (13, 10891): 993.5136642209292, (13, 10909): 987.8105119384736, (13, 10911): 983.4413384511254, (13, 10913): 983.6516908921991, (13, 10915): 980.8616582830466, (13, 10919): 979.4767842603343, (13, 11037): 1006.2956840923905, (13, 11039): 969.7612920884238, (13, 11516): 1139.046961274145, (13, 11856): 708.2939609248772, (13, 11857): 708.0318769578814, (13, 11861): 708.3448012399599, (13, 11881): 700.3261832851667, (13, 11902): 683.9014763002624, (13, 11911): 677.9239423854312, (13, 11914): 681.5059063298481, (13, 11922): 694.7614066933646, (13, 11924): 697.8740560371904, (13, 11926): 692.9588868259551, (13, 11950): 699.1546001148262, (13, 11963): 715.1461710805927, (13, 11983): 699.5409491197825, (13, 11985): 723.4280616418813, (13, 12009): 716.1071289424623, (13, 12010): 705.7855314497863, (13, 12018): 707.0875739311685, (13, 12020): 710.7656714289961, (13, 12021): 712.182013662402, (13, 12024): 723.0046932526348, (13, 12025): 720.1974041540863, (13, 12027): 717.4240039693959, (13, 12031): 703.9169460434432, (13, 12032): 708.3474738488048, (13, 12035): 714.4420245148713, (13, 12041): 727.3739916084259, (13, 12045): 573.3823392803102, (13, 12145): 637.531724827208, (13, 12275): 897.7342495014658, (13, 12294): 868.2292241752989, (13, 12358): 957.881358744124, (13, 12463): 992.6907471333999, (13, 12465): 991.6675819933502, (13, 12482): 1006.8102070179219, (13, 12503): 1004.693014025263, (13, 12506): 1008.8392062276384, (13, 12549): 999.9221215210907, (13, 12559): 996.7183377063385, (13, 12569): 1000.0921107394637, (13, 12572): 1003.2147055662907, (13, 12574): 996.6943867863002, (13, 12576): 1003.5638809893856, (13, 12591): 1002.9987985116629, (13, 12608): 1028.5586319402346, (13, 12696): 988.1234561347491, (13, 12710): 1012.4864466259496, (13, 12728): 1000.2718535369752, (13, 12766): 322.80199062830366, (13, 12771): 287.3980070585652, (13, 12790): 283.3621022525988, (13, 12795): 274.6119636567551, (13, 12797): 232.89748447432413, (13, 12798): 238.33368372219053, (13, 12811): 270.3212759204467, (13, 12830): 259.9577564854479, (13, 12848): 264.9783379609384, (13, 12850): 267.6560902228132, (13, 12852): 258.1981102332321, (13, 12854): 253.29334399516972, (13, 12859): 269.811627212234, (13, 12861): 243.67076169354942, (13, 12865): 276.6703261676123, (13, 12866): 273.9110698933848, (13, 12867): 283.9464438602786, (13, 12874): 279.10546713072273, (13, 12875): 282.71730834542626, (13, 12881): 267.7856379210235, (13, 12883): 273.8203797743363, (13, 12885): 285.98965277188074, (13, 12888): 270.8386972804371, (13, 12889): 269.3263875709741, (13, 12892): 280.2558831910451, (13, 12893): 271.23923711776104, (13, 12896): 273.98172953684644, (13, 12906): 280.45460199740904, (13, 13018): 255.28119211771562, (13, 13071): 262.45571156573493, (13, 13131): 202.5720007356604, (13, 13146): 231.3868220000223, (13, 13159): 220.0267151999189, (13, 13193): 195.29020376735127, (13, 13198): 134.29629915394878, (13, 13292): 198.1851279228814, (13, 13296): 216.74523821079663, (13, 13406): 116.81792206148324, (13, 13407): 117.31011872117148, (13, 13417): 132.83714497687524, (13, 13418): 140.46523823506354, (13, 13438): 145.53120306247544, (13, 13442): 144.88193302067316, (13, 13443): 141.33014836494004, (13, 13764): 412.1105848905393, (13, 13766): 407.15738132231263, (13, 13771): 419.2795493983653, (13, 13783): 404.4745346711104, (13, 13784): 398.6251848348454, (13, 13792): 439.7928457850272, (13, 13824): 409.3663624258008, (13, 14017): 339.803544419056, (13, 14870): 872.9449343008524, (13, 14997): 320.0574864110841, (13, 15000): 324.3256583655617, (13, 15003): 327.015796299599, (13, 15006): 302.2138483726976, (13, 15007): 300.7171754321195, (13, 15056): 315.0706943767664, (13, 15063): 319.5072672627163, (13, 15069): 325.52543178459746, (13, 15076): 303.72400741754365, (13, 15086): 304.1445895787331, (13, 15087): 312.7207907258088, (13, 15111): 314.81396063166375, (13, 15116): 313.9849041632669, (13, 15722): 380.2522664902422, (13, 15998): 524.5715817074718, (13, 16073): 1267.641310006868, (13, 16939): 1792.408357037751, (13, 16940): 1786.6126356310663, (13, 16951): 1792.0847241367028, (13, 16963): 1792.9185560402664, (13, 16965): 1800.4716487040535, (13, 16969): 1798.0555789122084, (13, 16970): 1795.8710517774364, (13, 16971): 1789.1063609258936, (13, 16973): 1788.250370396377, (13, 16974): 1803.1219628520023, (13, 16976): 1796.6519756000234, (13, 16978): 1791.851535422192, (13, 16980): 1799.4991458721158, (13, 16982): 1802.652083550634, (13, 17045): 1983.2900134331958, (13, 17048): 1991.8060159491538, (13, 17304): 831.8542768630595, (13, 17305): 825.7311037129209, (13, 17330): 830.2695166790533, (13, 17334): 824.1994646852042, (13, 17343): 835.9043614919805, (13, 17345): 821.7780356202114, (13, 17347): 828.3840272263773, (13, 17351): 813.3115366152157, (13, 17372): 822.4870098086482, (13, 17373): 835.7439825445111, (13, 17377): 836.509998191178, (13, 17382): 827.4211515368947, (13, 17383): 829.8085425423129, (13, 17389): 824.2821227835983, (13, 17400): 833.8657273986677, (13, 17401): 834.0189178831304, (13, 17402): 834.201092284326, (13, 17403): 834.9382271285989, (13, 17440): 820.1533754824814, (13, 17455): 832.9878708146559, (13, 17491): 832.4317238876001, (13, 17507): 824.136590434613, (13, 17509): 829.8504532661561, (13, 17590): 807.4781822694948, (13, 17615): 795.3484870721231, (13, 17642): 798.9421397569996, (13, 17643): 797.4128050810517, (13, 17668): 795.8567636910279, (13, 17721): 790.8183939780225, (13, 17754): 839.990885057255, (13, 17769): 828.6994959868593, (13, 17776): 803.8144612295442, (13, 17804): 837.4364825592289, (13, 17809): 842.5646977028748, (13, 17824): 840.8770113638128, (13, 17837): 818.5495709039432, (13, 17838): 817.7896879207863, (13, 17862): 813.3321114583666, (13, 17866): 824.93180459275, (13, 17872): 810.4206477440758, (13, 17873): 801.2632683574288, (13, 17881): 815.1183426734444, (13, 17947): 1334.1969751033055, (13, 17951): 1322.1191092127942, (13, 17953): 1320.3476138262174, (13, 17954): 1321.5454121700843, (13, 17959): 1330.7984310732488, (13, 17963): 1325.628324932961, (13, 18000): 1265.7526701167985, (13, 18001): 1268.8606065682588, (13, 18111): 1464.5397030943602, (13, 18148): 1169.1616786810603, (13, 18166): 1287.5508033465132, (13, 18189): 1389.4672458890832, (13, 18239): 839.1630162252421, (13, 18240): 838.8359320255856, (13, 18245): 839.510126791635, (13, 18247): 838.0937902937125, (13, 18251): 839.1687884117156, (13, 18256): 840.0286239110968, (13, 18258): 838.5758377981226, (13, 18259): 838.6698590843902, (13, 18260): 838.9796662456268, (13, 18262): 839.7612179346464, (13, 18263): 840.2213690166536, (13, 18264): 840.5458116018704, (13, 18266): 839.9180934430126, (13, 18267): 840.2747902491252, (13, 18268): 840.354926802648, (13, 18269): 841.0416036829124, (13, 18275): 840.7161711527838, (13, 18285): 840.5381157084296, (13, 18308): 833.52905633922, (13, 18313): 830.4140147752629, (13, 18314): 830.9632783498449, (13, 18315): 841.7127265692421, (13, 18316): 841.3038897890789, (13, 18317): 841.6030736461527, (13, 18320): 842.3804072498689, (13, 18321): 842.3900040377422, (13, 18322): 842.93161429473, (13, 18324): 843.8596156560095, (13, 18325): 846.0174702207667, (13, 18326): 845.2291222154705, (13, 18327): 841.5941728682297, (13, 18329): 847.3682871798329, (13, 18330): 845.233028990842, (13, 18331): 843.9527862783892, (13, 18332): 842.4607678707812, (13, 18333): 845.3075807089552, (13, 18336): 844.60540466546, (13, 18337): 845.5571793582542, (13, 18403): 842.5674541241793, (13, 18432): 803.9652842190991, (13, 18451): 829.9625723722559, (13, 18466): 856.6793663578982, (13, 18481): 843.1911238233982, (13, 18483): 842.9453711194394, (13, 18484): 841.9486660586828, (13, 18485): 839.2124906390317, (13, 18486): 843.2752768919399, (13, 18487): 840.8392242352836, (13, 18489): 842.0961652521233, (13, 18490): 845.5165225661204, (13, 18491): 846.8105953694933, (13, 18492): 837.8667471552582, (13, 18493): 843.1176176681552, (13, 18494): 841.3688421289335, (13, 18495): 844.5900565983876, (13, 18496): 843.0283991318137, (13, 18497): 840.5157494305691, (13, 18498): 840.1123972701358, (13, 18499): 842.0327118487055, (13, 18501): 841.0877585999434, (13, 18502): 839.890440763906, (13, 18503): 838.6631539564721, (13, 18504): 843.2562429711871, (13, 18506): 842.0017196662134, (13, 18507): 841.008830223453, (13, 18508): 842.0081867717697, (13, 18509): 842.2713273376304, (13, 18510): 839.0493218561732, (13, 18511): 844.0060959329646, (13, 18512): 842.073340083867, (13, 18515): 843.7268065132569, (13, 18516): 844.650596260036, (13, 18517): 843.5049780699351, (13, 18518): 845.4442518259643, (13, 18519): 843.3800148609602, (13, 18520): 841.3451457953005, (13, 18522): 848.1736283418571, (13, 18523): 848.7115803538593, (13, 18532): 850.8349956485393, (13, 18535): 846.6944845375374, (13, 18537): 844.3892955643222, (13, 18539): 845.0090092798275, (13, 18540): 845.4233073229625, (13, 18541): 846.6790634488507, (13, 18542): 847.4512492898042, (13, 18543): 843.7240293435286, (13, 18546): 845.9460104170051, (13, 18555): 849.5853467022331, (13, 18556): 850.4297558779483, (13, 18565): 850.9218085281556, (13, 18567): 852.5058966889566, (13, 18568): 850.2982611655086, (13, 18577): 864.4182629915877, (13, 18583): 861.3237794755596, (13, 18605): 863.4344564193019, (13, 18608): 854.797475540194, (13, 18616): 876.6643525469643, (13, 18618): 888.3775267840375, (13, 18625): 882.6647001015617, (13, 18645): 871.9892275261448, (13, 18646): 875.1737262454301, (13, 18653): 867.5567823612242, (13, 18654): 876.6846199031962, (13, 18655): 871.0732971466682, (13, 18666): 904.5135556707531, (13, 18837): 846.56456076936, (13, 18974): 824.8170958910248, (13, 18999): 831.9130413164155, (13, 19000): 835.243411349984, (13, 19174): 670.527968072833, (13, 19342): 737.4993997798841, (13, 19455): 698.9275645428363, (13, 19555): 533.8925342078275, (13, 19564): 545.5369990079932, (13, 19573): 537.9367034088065, (13, 19586): 534.4224971454153, (13, 19605): 536.7497516445148, (13, 19611): 541.7292112070613, (13, 19614): 539.0037479339004, (13, 19641): 619.8055476651244, (13, 19702): 619.0787732109088, (13, 19713): 612.9991002151229, (13, 19731): 507.1717733046588, (13, 19819): 673.1093057240059, (13, 19893): 660.5568622809242, (13, 19899): 708.5501398787018, (13, 19929): 668.9823993328343, (13, 19951): 749.7798195192407, (13, 19962): 683.518168671884, (13, 19970): 685.303453210861, (13, 19971): 689.2793046374695, (13, 19972): 685.1581136676052, (13, 19975): 679.4120828250104, (13, 19978): 751.1959806631464, (13, 19987): 750.3346668207603, (13, 19989): 728.1817684218347, (13, 20039): 753.3262652573923, (13, 20043): 759.5363888157885, (13, 20047): 749.7812155294566, (13, 20052): 727.7173208733061, (13, 20054): 731.0948560228178, (13, 20085): 822.8348092006132, (13, 20104): 829.167272345807, (13, 20132): 793.2876778820992, (13, 20203): 692.0685852085277, (13, 20280): 695.4426323649133, (13, 20285): 698.408975807857, (13, 20290): 696.7453893882594, (13, 20297): 688.6933787379267, (13, 20309): 781.2912580918354, (13, 20453): 871.0263575193441, (13, 20485): 639.3915620804295, (13, 20520): 618.5384221202166, (13, 20526): 624.9633255436648, (13, 20698): 670.356848310213, (13, 20868): 864.0127345526917, (13, 21042): 314.6154891490601, (13, 21057): 350.0808994661546, (13, 21066): 336.5215788846169, (13, 21075): 323.9942285560903, (13, 21093): 323.32232327219316, (13, 21098): 356.5357472555452, (13, 21127): 320.6625479353262, (13, 21130): 330.1226826709648, (13, 21144): 323.51010460116305, (13, 21146): 318.3966003115612, (13, 21147): 321.29086989685766, (13, 21148): 329.3227656022816, (13, 21153): 295.0949127039194, (13, 21293): 381.02028785137975, (13, 21426): 338.12415077012054, (13, 21442): 380.8303789709426, (13, 21451): 385.11818814647, (13, 21466): 359.7485740570861, (13, 21469): 366.7229276689683, (13, 21471): 356.18041003307326, (13, 21473): 362.12470710799096, (13, 21475): 357.00498867247603, (13, 21482): 370.5516904223451, (13, 21484): 369.3980487587305, (13, 21488): 365.15589746050443, (13, 21494): 357.8540107389637, (13, 21498): 362.81972194131845, (13, 21500): 355.7470769168447, (13, 21514): 373.70763091473697, (13, 21537): 356.8595264187878, (13, 21662): 383.50362035660646, (13, 21691): 357.5230695485156, (13, 21757): 300.41845825014695, (13, 21777): 278.8542862491196, (13, 21778): 274.22682100032193, (13, 21779): 281.0371383486452, (13, 21790): 279.76225560984045, (13, 21802): 287.5294646025781, (13, 21824): 296.54413567839396, (13, 21874): 287.47738998437796, (13, 21879): 292.9017911887268, (13, 21983): 272.74687372347546, (13, 22002): 354.57772554878954, (13, 22132): 252.52820717133508, (13, 22261): 826.0058056806683, (13, 22298): 819.8307378001472, (13, 22339): 910.205457434378, (13, 22508): 702.9522421579006, (13, 22841): 2079.369594223045, (13, 22842): 2079.546450743766, (13, 22874): 2063.544928026475, (13, 22941): 2064.7393418862116, (13, 22956): 2074.9427316013293, (13, 22960): 2077.5705314509705, (13, 22968): 2089.497366952523, (13, 22970): 2091.972675158577, (13, 22974): 2098.2178981233933, (13, 22980): 2110.339137022482, (13, 23025): 2110.993240878819, (13, 23028): 2108.681766775564, (13, 23081): 2131.522924375011, (13, 23104): 2113.276661812157, (13, 23147): 2000.2663736400357, (13, 23298): 495.4816602339859, (13, 23376): 477.19331449369537, (13, 23381): 473.87126833912487, (13, 23529): 512.6229542305604, (13, 23556): 501.23091094562295, (13, 23718): 479.29679690645963, (13, 24001): 604.4166766963955, (13, 24094): 647.7875684966959, (13, 24129): 666.1898390961362, (13, 24174): 632.51884681112, (13, 24235): 676.0042467358973, (13, 24259): 690.5186092008739, (13, 24260): 689.6342493708113, (13, 24261): 685.2931719785927, (13, 24305): 710.3785254033542, (13, 24306): 714.4771251057848, (13, 24307): 708.7940861502162, (13, 24308): 646.9596736813108, (13, 24498): 750.5369935662509, (13, 24499): 751.0861858737629, (13, 24500): 747.4667431751611, (13, 24668): 717.5529806935853, (13, 24711): 777.4392467890557, (13, 24756): 793.2890706306641, (13, 24788): 797.21135491525, (13, 24809): 780.0527397934592, (13, 24813): 785.0264459869805, (13, 24821): 783.2333685914847, (13, 24825): 785.210057557571, (13, 24832): 778.3751491632871, (13, 24833): 781.3381963836533, (13, 24835): 784.4931550262295, (13, 24837): 788.7569678913017, (13, 24840): 778.1631420653666, (13, 24841): 782.2365108436321, (13, 24844): 778.6337390976796, (13, 24845): 780.0381972607629, (13, 24846): 781.6073318356457, (13, 24849): 783.3799362512206, (13, 24850): 786.3278199297849, (13, 24863): 742.7667005185796, (13, 24866): 747.902890503816, (13, 24885): 755.2902507514813, (13, 24886): 756.4953473312222, (13, 24889): 765.4756485472374, (13, 24903): 768.9167943348873, (13, 24909): 747.8114230946977, (13, 24999): 983.1962418841015, (13, 25019): 975.6069505960492, (13, 25028): 980.0449578438976, (13, 25137): 761.8583364280855, (13, 25145): 766.5718804031682, (13, 25208): 871.3387101162472, (13, 25233): 866.1687059891858, (13, 25371): 729.8172494240524, (13, 25377): 705.6630220344719, (13, 25828): 480.34780196506927, (13, 25851): 433.75344151806036, (13, 25874): 458.09207183455334, (13, 25898): 496.5778194807667, (13, 25946): 476.64489386866524, (13, 26047): 580.6419995330742, (13, 26066): 539.8060778803023, (13, 26197): 538.6653471340609, (13, 26212): 566.0647445968325, (13, 26253): 578.3152954697218, (13, 26254): 571.0909020899784, (13, 26257): 574.823462852236, (13, 26258): 578.1253067524068, (13, 26260): 575.8083883930326, (13, 26266): 562.2861680960198, (13, 26267): 562.3205629815731, (13, 26271): 564.4821088459134, (13, 26304): 516.6718164404873, (13, 26305): 510.97758042227343, (13, 26363): 512.4172397347008, (13, 26441): 941.0621444436944, (13, 26442): 937.9415000783216, (13, 26450): 928.4888842752727, (13, 26459): 932.5403110227583, (13, 26462): 935.9945233419579, (13, 26467): 964.4952727935887, (13, 26471): 954.0859618308884, (13, 26472): 952.5370087608228, (13, 26473): 951.5321034349323, (13, 26476): 940.0369033895333, (13, 26485): 934.9817755092078, (13, 26493): 932.8270093654942, (13, 26524): 942.4141330719902, (13, 26525): 939.9761508407056, (13, 26556): 950.451339637318, (13, 26560): 953.4931769617866, (13, 26561): 948.2795614327314, (13, 26564): 946.7345553407198, (13, 26569): 945.4563406567313, (13, 26570): 941.4789777856646, (13, 26573): 940.9170941908953, (13, 26581): 938.8222385774236, (13, 26583): 937.8539589819376, (13, 26593): 936.5365689497646, (13, 26837): 964.5565685769031, (13, 26844): 971.9630154758172, (13, 26863): 951.3546817118319, (13, 26893): 970.8880404920737, (13, 26902): 980.8137903394186, (13, 26905): 974.7193127524997, (13, 26912): 981.1993588212682, (13, 26921): 960.9781037510973, (13, 26922): 934.8050400034655, (13, 27212): 1108.4323937848023, (13, 27218): 1104.5855987813693, (13, 27239): 1120.5921045048904, (13, 27257): 1112.266883230694, (13, 27274): 1122.3940981308197, (13, 27279): 1119.2616293656026, (13, 27282): 1111.6489846283423, (13, 27283): 1117.902065538317, (13, 27285): 1124.846210206455, (13, 27286): 1114.95805187423, (13, 27290): 1104.8724644363751, (13, 27295): 1102.7028265744805, (13, 27300): 1124.3651210904113, (13, 27344): 1096.4398041285476, (13, 27366): 1103.440925777553, (13, 27383): 1122.0326990302626, (13, 27398): 1135.3813266917257, (13, 27406): 1129.0091230699559, (13, 27407): 1132.5904503401923, (13, 27426): 1133.9818603685335, (13, 27432): 1097.7502478788304, (13, 27460): 1122.0007396745432, (13, 27523): 1080.4473510947296, (13, 27545): 1245.6162652049916, (13, 27602): 1411.9090455980465, (13, 27606): 1416.8081038033113, (13, 27646): 1205.999627434417, (13, 27667): 1240.3547846774873, (13, 27672): 1243.2350474121079, (13, 27674): 1236.702297961586, (13, 27688): 1245.8689899409862, (13, 27692): 1247.9601217175036, (13, 27693): 1242.581534394716, (13, 27705): 1241.091254106976, (13, 27712): 1242.7102067237158, (13, 27786): 1461.1216490243664, (13, 27790): 1456.058528590996, (13, 27791): 1456.5314724422806, (13, 27795): 1450.1494326391003, (13, 27801): 1445.0472459632294, (13, 27813): 1464.8374739567312, (13, 27816): 1461.354817161931, (13, 27823): 1444.9886904714358, (13, 27830): 1457.0008565757416, (13, 27884): 1135.9419722465514, (13, 27885): 1189.6525193590176, (13, 27896): 1157.874634836505, (13, 27919): 1156.8940847547617, (13, 27922): 1161.7720782113154, (13, 27930): 1145.6879574870754, (13, 27934): 1146.6547697191038, (13, 27935): 1146.9287826825973, (13, 27948): 1342.6434892206157, (13, 27951): 1368.9124732198045, (13, 28061): 1059.1971741698203, (13, 28290): 1470.0418058035111, (13, 28292): 1474.4590104105635, (13, 28293): 1470.5973411778289, (13, 28295): 1464.7781383770032, (13, 28296): 1468.3471630685665, (13, 28297): 1467.4506251937544, (13, 28302): 1462.3877540284573, (13, 28310): 1480.8362344674815, (13, 28313): 1485.3767970491563, (13, 28372): 1489.6431907736817, (13, 28398): 1490.033804730353, (13, 28399): 1487.2185539411994, (13, 28400): 1491.356067815128, (13, 28401): 1480.914401694621, (13, 28445): 1480.6086936726033, (13, 28475): 1475.0325180500215, (13, 28885): 692.1478942325322, (13, 28886): 689.494340662555, (13, 28915): 695.545745254575, (13, 28916): 691.663198706793, (13, 28917): 690.5194326555738, (13, 28921): 697.8543924742501, (13, 28931): 697.7088675481635, (13, 28945): 692.1679044788317, (13, 28982): 692.2519146739892, (13, 29219): 731.9517287601368, (13, 29228): 716.0628695560473, (13, 29246): 830.6223662836696, (13, 29248): 833.7017894241552, (13, 29282): 810.8234828361461, (13, 29290): 836.8752930450311, (13, 29291): 833.6672653383616, (13, 29292): 837.2832530472467, (13, 29293): 828.5483624050086, (13, 29294): 837.3256237077221, (13, 29298): 830.3471106679877, (13, 29299): 830.7665923098235, (13, 29304): 820.0472339878526, (13, 29317): 797.5983106518039, (13, 29323): 795.7268082122667, (13, 29330): 806.7381574999446, (13, 29331): 811.2520054758097, (13, 29344): 742.7885633995545, (13, 29445): 590.296886650146, (13, 29724): 2042.536844131813, (13, 29738): 2045.7815548179378, (13, 29745): 2035.9946948872896, (13, 29748): 2036.2774135546106, (13, 29750): 2040.9304187436214, (13, 29759): 2032.0209385510227, (13, 29772): 2043.9850732972554, (13, 29781): 2041.328218897555, (13, 29784): 2039.9545068880257, (13, 29790): 2043.6595504151403, (13, 29811): 2036.1703332803925, (13, 29817): 2054.553507655279, (13, 29818): 2051.9520563833194, (13, 29929): 2035.8826319801294, (13, 30039): 2083.0180570311886, (13, 30066): 2058.668472376969, (13, 30116): 1944.240197331326, (13, 30238): 1775.6999526603984, (13, 30248): 1863.3719588421163, (13, 30260): 1865.7140067053926, (13, 30545): 628.2521966483034, (13, 30733): 451.4017635964633, (13, 30756): 432.9109038866537, (13, 30921): 501.4053059076784, (13, 31079): 151.5458385220574, (13, 31149): 94.13536905498569, (13, 31154): 103.07078347056773, (13, 31160): 92.78259211157597, (13, 31163): 102.62568746518636, (13, 31189): 104.00479508238851, (13, 31215): 108.1838211738366, (13, 31259): 143.73538985643071, (13, 31262): 143.85749091321608, (13, 31430): 180.32532553938, (13, 31568): 265.365395522902, (13, 31751): 161.50299361490863, (15, 109): 578.1413317564536, (15, 872): 1956.9381908603093, (15, 873): 1965.0829672519126, (15, 877): 1961.999477690181, (15, 879): 1963.2052119894686, (15, 884): 1954.9613868133908, (15, 889): 1960.0796838215817, (15, 891): 1952.272486281871, (15, 892): 1969.5255380632232, (15, 894): 1968.5082034793675, (15, 896): 1960.7082445511624, (15, 903): 1962.2747939821982, (15, 909): 1948.5007466019915, (15, 910): 1951.7913256044264, (15, 912): 1946.3982317147538, (15, 913): 1940.4446610514815, (15, 916): 1937.9701492160993, (15, 926): 1954.5026247196186, (15, 927): 1951.7755371413555, (15, 948): 1949.3236956152316, (15, 961): 1954.140510676533, (15, 962): 1955.0853099352903, (15, 963): 1956.1408970797963, (15, 967): 1965.7298428942897, (15, 974): 1961.2993931464887, (15, 998): 1968.9325454533523, (15, 1014): 2147.274471371639, (15, 1086): 1937.9857048969238, (15, 1087): 1937.1081154727324, (15, 1089): 1929.5196619878363, (15, 1090): 1932.9388561805793, (15, 1092): 1944.6720361469188, (15, 1097): 1935.693825750926, (15, 1107): 1950.6049210310691, (15, 1387): 729.829922668674, (15, 1554): 603.5091873578338, (15, 1827): 2328.765758722112, (15, 1828): 2329.648869771056, (15, 1829): 2330.892095972326, (15, 1830): 2329.5264652836327, (15, 1831): 2330.2720553555378, (15, 1832): 2329.39908380486, (15, 1833): 2329.509967385151, (15, 1836): 2328.5815293144647, (15, 1841): 2333.8008452128524, (15, 1843): 2331.606553668469, (15, 1844): 2332.571483980065, (15, 1845): 2329.948333669307, (15, 1847): 2321.5270991911957, (15, 1848): 2324.434694797206, (15, 1849): 2338.050734868617, (15, 1850): 2339.4890578222544, (15, 1851): 2326.6278164392984, (15, 1852): 2326.813674966108, (15, 1854): 2328.227819485398, (15, 1856): 2321.076713509262, (15, 1857): 2324.2208787582067, (15, 1858): 2336.744775943835, (15, 1861): 2330.6841787747317, (15, 1866): 2320.8673980770986, (15, 1867): 2333.97564432115, (15, 1868): 2332.237073837715, (15, 1870): 2332.2946298400675, (15, 1871): 2333.6012922968384, (15, 1875): 2328.098669193598, (15, 1880): 2322.923310781023, (15, 1882): 2323.743976875096, (15, 1883): 2339.6330741796683, (15, 1889): 2324.4907422422225, (15, 1893): 2331.097010450682, (15, 1894): 2329.0458683761685, (15, 1899): 2322.694091749045, (15, 1900): 2324.2211515711388, (15, 1902): 2334.669771747001, (15, 1905): 2337.307449347615, (15, 1907): 2326.4430291976255, (15, 1910): 2327.456929920251, (15, 1917): 2342.9894308826465, (15, 1920): 2326.666664558138, (15, 1935): 2337.7242523206446, (15, 1937): 2339.9782020193625, (15, 1946): 2318.1812693081956, (15, 1949): 2320.728137267457, (15, 1950): 2311.764823747043, (15, 1951): 2316.0754976655026, (15, 1952): 2319.2247696033864, (15, 1953): 2320.680276400775, (15, 1954): 2318.6139660307167, (15, 1958): 2319.9799967268073, (15, 1960): 2324.267878151977, (15, 1968): 2325.960253652397, (15, 1969): 2338.295289191179, (15, 1974): 2335.0651591776846, (15, 1975): 2335.0162535169843, (15, 1979): 2328.9295703402718, (15, 1980): 2328.4080978923425, (15, 1981): 2330.220967545912, (15, 1985): 2331.7046157117147, (15, 1994): 2308.214836407147, (15, 2011): 2323.6230481322764, (15, 2019): 2344.9338072224314, (15, 2020): 2342.114980498042, (15, 2029): 2331.3826710041226, (15, 2030): 2340.161746532011, (15, 2032): 2329.6127654476286, (15, 2033): 2335.3286110629188, (15, 2034): 2335.2149076101014, (15, 2036): 2324.4305834203196, (15, 2037): 2327.192441543844, (15, 2038): 2328.185031505374, (15, 2042): 2360.7317949246954, (15, 2050): 2333.88528356676, (15, 2051): 2333.3990192526708, (15, 2053): 2334.2701466081476, (15, 2054): 2337.149177613539, (15, 2066): 2331.2874274966393, (15, 2067): 2331.314703984301, (15, 2071): 2302.7928888183305, (15, 2072): 2308.20097718648, (15, 2073): 2293.4297710063893, (15, 2074): 2292.6887487510994, (15, 2080): 2283.548947462385, (15, 2082): 2311.114032598269, (15, 2083): 2313.9114076761953, (15, 2089): 2307.9962238255835, (15, 2090): 2310.6079674769153, (15, 2092): 2307.0614081235954, (15, 2098): 2287.0530612317384, (15, 2099): 2290.19090542126, (15, 2101): 2286.476919089092, (15, 2102): 2301.217395632436, (15, 2103): 2296.5796946040755, (15, 2104): 2294.0401352527983, (15, 2106): 2315.793241194931, (15, 2112): 2288.4304744876895, (15, 2113): 2303.31147334678, (15, 2114): 2306.8538660287204, (15, 2117): 2318.0002155026245, (15, 2123): 2296.764732777681, (15, 2124): 2299.80390257098, (15, 2134): 2291.1329024909355, (15, 2138): 2300.07951293652, (15, 2141): 2292.189321148791, (15, 2148): 2296.6069445192697, (15, 2150): 2284.790473093993, (15, 2151): 2287.986468005702, (15, 2152): 2283.1075132909305, (15, 2153): 2297.634685588781, (15, 2154): 2285.043737330755, (15, 2155): 2283.590897096281, (15, 2156): 2281.250130393532, (15, 2157): 2284.437604489121, (15, 2160): 2304.3131249734765, (15, 2161): 2282.579852631022, (15, 2162): 2298.1588569940227, (15, 2163): 2293.8897556232782, (15, 2164): 2293.6033357561573, (15, 2168): 2286.0040116799364, (15, 2172): 2288.8345493388583, (15, 2174): 2287.6148258182684, (15, 2178): 2291.3270827900847, (15, 2179): 2289.360995768336, (15, 2183): 2299.8679219151736, (15, 2185): 2300.057557880946, (15, 2186): 2297.6325430828647, (15, 2190): 2304.911292947802, (15, 2192): 2300.543946247278, (15, 2193): 2300.7209962333527, (15, 2194): 2296.2602802781457, (15, 2195): 2295.611312520595, (15, 2197): 2301.49905539059, (15, 2205): 2295.253399082337, (15, 2207): 2287.1268037679433, (15, 2208): 2291.671733587863, (15, 2212): 2302.0332321847254, (15, 2214): 2211.933978291173, (15, 2225): 2222.6251681128697, (15, 2231): 2201.679011825206, (15, 2278): 2267.0124785424964, (15, 2284): 2276.190255692293, (15, 2285): 2274.9058330104754, (15, 2291): 2256.66987270554, (15, 2292): 2258.6681978397633, (15, 2307): 2270.222073585812, (15, 2313): 2254.51168819843, (15, 2317): 2251.8949786752064, (15, 2319): 2261.8252453507475, (15, 2321): 2266.0379211589984, (15, 2323): 2265.4883600202625, (15, 2326): 2281.5582568775876, (15, 2327): 2277.5835233686416, (15, 2329): 2274.8695784834563, (15, 2330): 2271.775628525221, (15, 2332): 2278.3196291969775, (15, 2344): 2268.1975950035453, (15, 2346): 2268.0047889436887, (15, 2361): 2266.5384571839586, (15, 2368): 2312.849846711963, (15, 2374): 2317.2185570154948, (15, 2375): 2318.685976469726, (15, 2377): 2303.418915834565, (15, 2378): 2321.438238800859, (15, 2379): 2321.8150142463346, (15, 2380): 2323.32922289461, (15, 2383): 2307.499027271436, (15, 2385): 2309.8605077593083, (15, 2395): 2310.131634403317, (15, 2397): 2319.9952832029867, (15, 2398): 2298.5542944408594, (15, 2399): 2304.0537402424693, (15, 2400): 2302.8217387059326, (15, 2402): 2311.5182024966684, (15, 2403): 2314.931395235289, (15, 2404): 2315.814921467327, (15, 2405): 2307.5855357800665, (15, 2407): 2314.295839917165, (15, 2408): 2318.2967748550777, (15, 2409): 2310.0834624299773, (15, 2411): 2314.8886308337183, (15, 2412): 2313.999593222432, (15, 2413): 2316.797523719361, (15, 2414): 2312.2421705467714, (15, 2422): 2313.842901504332, (15, 2424): 2314.967204970642, (15, 2426): 2315.7106001520883, (15, 2433): 2309.3402838927077, (15, 2436): 2307.6348535962056, (15, 2437): 2287.706736849366, (15, 2440): 2292.102228802533, (15, 2445): 2380.170997594263, (15, 2447): 2369.339256976953, (15, 2454): 2379.5482945987583, (15, 2455): 2380.1293082688267, (15, 2460): 2348.4100901169836, (15, 2461): 2352.3219674022607, (15, 2471): 2415.5046353934986, (15, 2492): 2347.797182509218, (15, 2511): 2316.133256665993, (15, 2523): 2332.322171353393, (15, 2525): 2327.494400455631, (15, 2535): 2336.1968382908, (15, 2537): 2329.1658416586274, (15, 2538): 2334.0479659682724, (15, 2539): 2331.8472836129067, (15, 2540): 2339.3826641692685, (15, 2542): 2344.4204557400817, (15, 2559): 2444.529642183492, (15, 2575): 2435.3142937889615, (15, 2599): 2284.749008058167, (15, 2600): 2318.4377297889027, (15, 2607): 2299.118972402715, (15, 2627): 2335.238397592482, (15, 2647): 2353.740181885073, (15, 2674): 2344.3270055746743, (15, 2681): 2341.6753756455646, (15, 2683): 2350.7762246155044, (15, 2686): 2340.394508369167, (15, 2689): 2461.3483383865464, (15, 2690): 2461.922705699193, (15, 2713): 2485.055775403592, (15, 2714): 2487.075692907349, (15, 2715): 2490.056627443037, (15, 2739): 2487.417217064733, (15, 2740): 2468.667585260528, (15, 2741): 2470.1551307728105, (15, 2749): 2483.2856756718325, (15, 2750): 2484.222225673499, (15, 2752): 2486.3502373163833, (15, 2755): 2488.704916022238, (15, 2758): 2488.0132252442068, (15, 2759): 2488.025362753518, (15, 2769): 2484.567019629644, (15, 2771): 2473.464788610343, (15, 2779): 2474.3552530394563, (15, 2784): 2440.76739009975, (15, 2800): 2446.768197716103, (15, 2802): 2462.869072259934, (15, 2803): 2461.738706711585, (15, 2804): 2459.747304587189, (15, 2805): 2465.371016201366, (15, 2807): 2465.187937342123, (15, 2809): 2464.0710424835697, (15, 2812): 2444.932634167505, (15, 2814): 2463.0545636312186, (15, 2817): 2463.7236250302026, (15, 2819): 2465.5860784645015, (15, 2823): 2446.77642221408, (15, 2832): 2469.074232037396, (15, 2836): 2455.6374041313607, (15, 2839): 2465.1484443329045, (15, 2841): 2464.3782690813237, (15, 2843): 2463.378454280493, (15, 2846): 2458.2812634085944, (15, 2849): 2471.166821629066, (15, 2852): 2468.1167504012474, (15, 2853): 2472.570653331372, (15, 2876): 2473.923579195215, (15, 2877): 2484.702809459646, (15, 2885): 2487.973438104743, (15, 2918): 2467.136254036367, (15, 2921): 2471.7691495581516, (15, 2925): 2450.0382114615713, (15, 2926): 2442.791728858447, (15, 2930): 2459.13335771682, (15, 2931): 2452.032146700311, (15, 2938): 2467.1895029534644, (15, 2940): 2480.6898016327145, (15, 2947): 2464.8586190476267, (15, 2949): 2459.0066101913003, (15, 2950): 2461.087344150549, (15, 2952): 2458.7975673517044, (15, 2958): 2458.352882126106, (15, 2959): 2460.5652373516, (15, 2960): 2465.6635066718136, (15, 2961): 2463.21286807847, (15, 2963): 2456.4109360036728, (15, 2968): 2457.866120997279, (15, 2976): 2455.804060341666, (15, 2981): 2412.246041112037, (15, 2982): 2410.996839072816, (15, 2984): 2408.73316628234, (15, 3003): 2404.762758920994, (15, 3046): 2375.0702775440855, (15, 3050): 2398.3734835083587, (15, 3051): 2400.163964579417, (15, 3053): 2395.166634289171, (15, 3069): 2423.11350109683, (15, 3071): 2393.9543290385677, (15, 3080): 2488.058937524078, (15, 3199): 2397.4684489802275, (15, 3200): 2392.207974477205, (15, 3205): 2424.719309194525, (15, 3209): 2394.968270833594, (15, 3215): 2392.518548040918, (15, 3217): 2386.026121327364, (15, 3249): 2393.0927203462334, (15, 3263): 2442.1095214842735, (15, 3289): 2408.534809638667, (15, 3301): 2410.135055516046, (15, 3302): 2407.780042125624, (15, 3307): 2404.860527429848, (15, 3310): 2412.9299024162774, (15, 3391): 2420.18904704663, (15, 3509): 1362.1307877287313, (15, 3510): 1357.489453560068, (15, 3511): 1360.5944267538741, (15, 3512): 1357.7369194187715, (15, 3514): 1358.7257282749374, (15, 3519): 1372.9781630058233, (15, 3536): 1370.3437885177316, (15, 3545): 1377.6430594896524, (15, 3548): 1370.5501010732924, (15, 3572): 1372.9619127925744, (15, 3581): 1367.3041064003162, (15, 3583): 1364.1901034471507, (15, 3601): 1381.6938106912926, (15, 3656): 1374.172548266903, (15, 3669): 1365.2213978969885, (15, 3670): 1369.3940461514537, (15, 3695): 1345.5306710555108, (15, 3696): 1348.8182151936082, (15, 3782): 1372.8170618675704, (15, 3792): 1367.5968178930943, (15, 3989): 633.9821444182481, (15, 4008): 659.5925577984518, (15, 4031): 659.9203599495322, (15, 4045): 648.9261650548987, (15, 4144): 648.7203231698949, (15, 4145): 621.7365950152036, (15, 4164): 638.4953596158658, (15, 4168): 629.8875066564297, (15, 4173): 627.9690270841897, (15, 4181): 612.4673047645335, (15, 4228): 599.1810483503239, (15, 4248): 591.0855332378065, (15, 4254): 456.4073244367827, (15, 4260): 456.10584879738036, (15, 4262): 465.1169784588069, (15, 4273): 462.7942793840561, (15, 4319): 390.91180978910893, (15, 4326): 388.0311017061959, (15, 4328): 388.512281351803, (15, 4334): 394.56761891752006, (15, 4335): 393.12195625606114, (15, 4372): 812.9099017695123, (15, 4413): 889.6982203755688, (15, 4434): 806.0117763308849, (15, 4447): 800.74743038985, (15, 4452): 808.9545120145627, (15, 4463): 788.2567341292038, (15, 4465): 785.7966950169059, (15, 4619): 937.3192615050611, (15, 4645): 940.7897008573314, (15, 4657): 944.2854607078049, (15, 4666): 945.0261741667352, (15, 4676): 951.6928542186608, (15, 4678): 950.8150576932295, (15, 4689): 952.2245266816262, (15, 4704): 987.2821551385222, (15, 4726): 1177.3783261648055, (15, 4727): 1174.3072807960798, (15, 4730): 1168.0467214080559, (15, 4731): 1171.8551164987193, (15, 4734): 1163.7309819861298, (15, 4735): 1162.5443717319472, (15, 4736): 1165.5130201308764, (15, 4737): 1162.3901998131785, (15, 4738): 1164.2937083482482, (15, 4756): 1168.2863781241415, (15, 4760): 1144.414882529408, (15, 4761): 1142.7611157644972, (15, 4762): 1142.2779527871055, (15, 4765): 1146.9426756005714, (15, 4773): 1181.7506782567457, (15, 4774): 1181.7439720299703, (15, 4790): 1179.3013122990146, (15, 4795): 1175.9354614376361, (15, 4799): 1184.5177044771042, (15, 4801): 1194.677108837158, (15, 4804): 1173.563994317851, (15, 4805): 1170.8376667700306, (15, 4806): 1184.612315878234, (15, 4815): 1184.0856323122869, (15, 4816): 1190.5147220697825, (15, 4817): 1195.1800811405985, (15, 4826): 1189.6433195207478, (15, 4830): 1186.6400850761381, (15, 4839): 1153.516619944229, (15, 4840): 1157.6118991328142, (15, 4841): 1152.2487065362898, (15, 4846): 1149.5869842358386, (15, 4848): 1151.6276654197736, (15, 4850): 1154.8796899656581, (15, 4871): 1106.7492716276147, (15, 4883): 1136.9745673099308, (15, 4900): 1117.5769079214483, (15, 4901): 1115.9484278854054, (15, 4917): 994.1138261376061, (15, 4931): 976.4561595360851, (15, 4944): 993.92960960187, (15, 4956): 981.8910401994983, (15, 4958): 985.7546168457611, (15, 4959): 985.4292844805085, (15, 4961): 983.6745734895579, (15, 4966): 980.1351359731461, (15, 5207): 961.270271533616, (15, 5272): 493.9706222610789, (15, 5283): 500.87321651257895, (15, 5287): 524.8291768654943, (15, 5289): 528.3596707723574, (15, 5293): 482.4767931859665, (15, 5295): 500.27662012596664, (15, 5296): 507.96976072458585, (15, 5298): 512.1212260839796, (15, 5303): 524.0733189713211, (15, 5305): 505.8603075175483, (15, 5306): 512.4600225817811, (15, 5307): 503.3592037259821, (15, 5308): 511.293010047686, (15, 5313): 500.9773029782951, (15, 5314): 501.9038842783004, (15, 5317): 516.5333044815105, (15, 5319): 519.8359491124676, (15, 5324): 510.25957764081187, (15, 5326): 503.62881391262454, (15, 5348): 517.9674095562447, (15, 5351): 533.6373895433359, (15, 5399): 543.3502322650909, (15, 5413): 558.924374386631, (15, 5422): 539.003125474812, (15, 5445): 528.2437402754073, (15, 5448): 522.5392358839126, (15, 5456): 529.6075676935069, (15, 5467): 537.0875037405318, (15, 5624): 450.37076397897135, (15, 5671): 549.5596702042426, (15, 5672): 538.9461029661088, (15, 5797): 672.4451282147081, (15, 5871): 698.5548635045615, (15, 5976): 633.1912505824986, (15, 6118): 1928.4530656414167, (15, 6248): 2031.9050799137083, (15, 6345): 345.51646980091607, (15, 6352): 368.9984374620166, (15, 6354): 338.7923402032964, (15, 6359): 335.9109529932358, (15, 6376): 369.72221322279944, (15, 6378): 341.776276267, (15, 6381): 339.08711676824794, (15, 6383): 349.7974213011698, (15, 6396): 349.3431637783106, (15, 6399): 347.3828800810982, (15, 6408): 366.4106757487788, (15, 6409): 351.00807668328883, (15, 6419): 382.62540656273984, (15, 6422): 359.86676059995614, (15, 6423): 361.5220844687053, (15, 6424): 336.15103662338703, (15, 6439): 339.30909866463566, (15, 6464): 344.5316909322257, (15, 6465): 348.26287403575236, (15, 6469): 348.4202571470597, (15, 6470): 350.5938176030459, (15, 6472): 328.653516782395, (15, 6480): 326.03482482233045, (15, 6486): 305.2789597819331, (15, 6497): 311.7712079058593, (15, 6503): 335.5901510413313, (15, 6508): 337.7693975589881, (15, 6509): 331.46192872333785, (15, 6521): 320.0514876706323, (15, 6544): 317.71084889567516, (15, 6552): 348.7066317451445, (15, 6553): 351.9268519623719, (15, 6554): 355.257173665216, (15, 6578): 343.9108453767589, (15, 6582): 342.42416201375147, (15, 6601): 341.5505217299048, (15, 6609): 319.55494347112375, (15, 6610): 317.5964330462626, (15, 6611): 319.60302878177646, (15, 6614): 322.98287417780944, (15, 6615): 321.4016054954256, (15, 6616): 314.43954474844986, (15, 6617): 317.1721678006886, (15, 6618): 308.8367902780705, (15, 6619): 324.83752059244125, (15, 6620): 312.77361677144506, (15, 6621): 315.3152627818661, (15, 6622): 315.73230488125654, (15, 6623): 321.41831065547376, (15, 6624): 322.2200212816227, (15, 6625): 323.6383120102372, (15, 6626): 325.7501702939912, (15, 6627): 325.2173435027199, (15, 6628): 311.79900502144505, (15, 6629): 319.46763755072806, (15, 6630): 328.78708404672403, (15, 6632): 320.6372920118994, (15, 6634): 330.7663201358839, (15, 6635): 317.1876486569205, (15, 6636): 313.7209721255902, (15, 6637): 323.22573133168953, (15, 6638): 326.82205874830896, (15, 6639): 323.89387208142256, (15, 6640): 327.19843093883065, (15, 6641): 314.19222416247953, (15, 6642): 325.6499317550511, (15, 6643): 327.32033390733216, (15, 6645): 323.6644874942663, (15, 6646): 311.10672277572763, (15, 6647): 325.40323316161727, (15, 6653): 322.060468430595, (15, 6655): 324.4335204289487, (15, 6658): 330.324103541224, (15, 6662): 324.6514341636824, (15, 6819): 474.8703554802822, (15, 6996): 411.06548488153317, (15, 7059): 372.4375228698278, (15, 7187): 458.5149618396365, (15, 7304): 521.8172870786759, (15, 7528): 417.235656557058, (15, 7720): 186.41856705089933, (15, 7793): 195.07088428461802, (15, 7807): 190.389216491542, (15, 7808): 197.51880750476926, (15, 7831): 288.43880682923685, (15, 7850): 260.18998288917874, (15, 7852): 270.79686289791164, (15, 8012): 197.11323725309947, (15, 8125): 229.71403751241095, (15, 8208): 119.02077857772102, (15, 8392): 247.56694975147076, (15, 8651): 659.7512762848712, (15, 9088): 510.1817843873885, (15, 9443): 751.2662408742078, (15, 9444): 746.4633280265605, (15, 9828): 933.8508019548146, (15, 9868): 923.0329110392155, (15, 10180): 235.87431663537663, (15, 10256): 206.9625305959824, (15, 10276): 197.04935065417405, (15, 10378): 136.8652253920794, (15, 10676): 333.26500219225596, (15, 10714): 387.5998677019489, (15, 10730): 325.9767221728489, (15, 10862): 952.1191106925606, (15, 10881): 953.6089401739564, (15, 10883): 955.8068721072696, (15, 10885): 951.229689712489, (15, 10891): 959.2939807619872, (15, 10909): 953.5087866971793, (15, 10911): 947.9156262138572, (15, 10913): 949.4407161187676, (15, 10915): 946.4306016009124, (15, 10919): 944.1244446877722, (15, 11037): 1009.3718605861517, (15, 11039): 984.1555908789311, (15, 11516): 936.4170749800882, (15, 11856): 396.94074572543235, (15, 11857): 395.2548562702455, (15, 11861): 396.23541687214293, (15, 11881): 389.9105505964376, (15, 11902): 373.04026445932965, (15, 11911): 368.52818254211695, (15, 11914): 371.4789849480701, (15, 11922): 384.53637546702026, (15, 11924): 388.14454199904196, (15, 11926): 383.1937681037347, (15, 11950): 391.42637391100095, (15, 11963): 407.54630156764404, (15, 11983): 394.9535191999506, (15, 11985): 415.739811929975, (15, 12009): 411.0264318468092, (15, 12010): 399.9459288088958, (15, 12018): 401.63886553357776, (15, 12020): 404.93916996345865, (15, 12021): 406.6744543880133, (15, 12024): 417.58125503209425, (15, 12025): 414.1896370475297, (15, 12027): 411.5315013682899, (15, 12031): 398.04512643362676, (15, 12032): 402.0744129241924, (15, 12035): 410.0119255693848, (15, 12041): 418.2913476974715, (15, 12045): 264.764027415987, (15, 12145): 333.3333163928725, (15, 12275): 649.8129647483076, (15, 12294): 627.6344250358536, (15, 12358): 716.4236207577155, (15, 12463): 754.2010096618146, (15, 12465): 753.5392485699537, (15, 12482): 763.3913281682899, (15, 12503): 762.4753303269554, (15, 12506): 766.2608600434152, (15, 12549): 753.0632597104569, (15, 12559): 751.1298525070396, (15, 12569): 756.0091080568008, (15, 12572): 758.7612950735405, (15, 12574): 752.4566569802981, (15, 12576): 755.8035716389339, (15, 12591): 752.4502736356188, (15, 12608): 773.9779500944194, (15, 12696): 734.8761032351948, (15, 12710): 753.7616510742283, (15, 12728): 746.3265390749687, (15, 12766): 237.56157162405088, (15, 12771): 195.93615775563882, (15, 12790): 196.9424457856687, (15, 12795): 204.2553498690057, (15, 12797): 183.44896016496276, (15, 12798): 181.28167938179993, (15, 12811): 182.47961688021468, (15, 12830): 188.5022737733462, (15, 12848): 174.62758118253797, (15, 12850): 166.2470663465983, (15, 12852): 184.15095736848986, (15, 12854): 184.0626508488159, (15, 12859): 171.2483996966994, (15, 12861): 177.7822607533759, (15, 12865): 189.46515903954224, (15, 12866): 184.94151917970854, (15, 12867): 190.12252337468087, (15, 12874): 188.13574986102378, (15, 12875): 186.89477455163552, (15, 12881): 189.88044295263248, (15, 12883): 189.97991687033576, (15, 12885): 188.39945904449866, (15, 12888): 186.9092473864576, (15, 12889): 184.03193822529926, (15, 12892): 189.90630282708133, (15, 12893): 189.82300760415438, (15, 12896): 187.19068825271182, (15, 12906): 201.0201508469203, (15, 13018): 274.6533099972785, (15, 13071): 291.05108022617213, (15, 13131): 233.14410952074516, (15, 13146): 212.7097152278001, (15, 13159): 304.85659418854056, (15, 13193): 230.4177699297835, (15, 13198): 231.52921655120514, (15, 13292): 194.15836181824378, (15, 13296): 160.19637949744907, (15, 13406): 288.71912400102235, (15, 13407): 292.7303891785214, (15, 13417): 318.74751894094464, (15, 13418): 319.39103821176195, (15, 13438): 287.2267713522581, (15, 13442): 276.4263184919399, (15, 13443): 279.96828937044233, (15, 13764): 725.429392496686, (15, 13766): 720.1073353847477, (15, 13771): 731.7786379419024, (15, 13783): 719.3082039164659, (15, 13784): 711.5168789258105, (15, 13792): 751.8096189653447, (15, 13824): 724.2605058620893, (15, 14017): 656.8615287003468, (15, 14870): 830.9375823512828, (15, 14997): 488.5386018245745, (15, 15000): 489.1798633758555, (15, 15003): 486.62030011456056, (15, 15006): 472.6524976576316, (15, 15007): 468.830066050519, (15, 15056): 472.9399560538564, (15, 15063): 477.1736966187173, (15, 15069): 480.0049977470947, (15, 15076): 469.0101949555994, (15, 15086): 479.9785851686687, (15, 15087): 485.71350585399824, (15, 15111): 496.53045034635056, (15, 15116): 490.4035711913601, (15, 15722): 595.4426549335795, (15, 15998): 696.9457522490166, (15, 16073): 1585.4227004082873, (15, 16939): 2069.314157823997, (15, 16940): 2063.3009425125647, (15, 16951): 2070.073376065312, (15, 16963): 2070.668883708291, (15, 16965): 2078.0202743838604, (15, 16969): 2076.1993613218033, (15, 16970): 2073.3441406250863, (15, 16971): 2066.722831465467, (15, 16973): 2066.254230111698, (15, 16974): 2080.9514552370147, (15, 16976): 2073.8736836352846, (15, 16978): 2069.0449762391722, (15, 16980): 2076.343513377235, (15, 16982): 2080.874957482336, (15, 17045): 2284.2158606735634, (15, 17048): 2292.7477352982855, (15, 17304): 553.6876306440748, (15, 17305): 550.1704439242063, (15, 17330): 553.9477755599235, (15, 17334): 545.3418212501738, (15, 17343): 560.2745534739906, (15, 17345): 545.7557128501237, (15, 17347): 553.9232122200527, (15, 17351): 534.1544474489126, (15, 17372): 544.6714296314509, (15, 17373): 559.6690799891468, (15, 17377): 560.788829974779, (15, 17382): 551.173191111557, (15, 17383): 552.7066908743647, (15, 17389): 547.093641242564, (15, 17400): 556.7572915050418, (15, 17401): 556.4543748724418, (15, 17402): 557.3957895732742, (15, 17403): 558.414478175494, (15, 17440): 547.3348992327694, (15, 17455): 559.1643080953042, (15, 17491): 560.8212177942319, (15, 17507): 538.7085342059237, (15, 17509): 543.9817729403134, (15, 17590): 531.4017592612526, (15, 17615): 500.99594930958926, (15, 17642): 506.02366642844703, (15, 17643): 505.40232818098053, (15, 17668): 500.93191662194266, (15, 17721): 490.54496101455675, (15, 17754): 540.6663281417009, (15, 17769): 540.443351277415, (15, 17776): 519.4544747909571, (15, 17804): 549.0738256170908, (15, 17809): 554.3952758827177, (15, 17824): 551.0444362248508, (15, 17837): 535.7160498108473, (15, 17838): 536.5138519854195, (15, 17862): 532.672998446579, (15, 17866): 543.899465797555, (15, 17872): 528.6868135746561, (15, 17873): 520.1652628324925, (15, 17881): 533.2816401040902, (15, 17947): 1578.2146640427181, (15, 17951): 1566.782937980167, (15, 17953): 1564.587256229415, (15, 17954): 1565.3804225105484, (15, 17959): 1575.8860343302338, (15, 17963): 1571.8858325756091, (15, 18000): 1513.7451829547497, (15, 18001): 1516.0013848329968, (15, 18111): 1680.6325679585427, (15, 18148): 1387.8684771482124, (15, 18166): 1501.797173043757, (15, 18189): 1606.7441075438562, (15, 18239): 562.1020931746642, (15, 18240): 562.0882700992512, (15, 18245): 562.6272231797903, (15, 18247): 561.5120588475722, (15, 18251): 562.6695394171178, (15, 18256): 563.9877693352756, (15, 18258): 562.6789198472026, (15, 18259): 562.9516833403615, (15, 18260): 563.5172099543367, (15, 18262): 564.5499891058653, (15, 18263): 564.3718435181911, (15, 18264): 564.9295840406537, (15, 18266): 565.0036346279466, (15, 18267): 565.5448505939005, (15, 18268): 565.8358958100048, (15, 18269): 566.9255213489223, (15, 18275): 566.4113488176579, (15, 18285): 564.7170205366713, (15, 18308): 553.5747799560456, (15, 18313): 549.9412746306426, (15, 18314): 551.6908894194389, (15, 18315): 566.6876171001442, (15, 18316): 566.6855221122154, (15, 18317): 567.1999197898411, (15, 18320): 567.5569962050795, (15, 18321): 567.8785286810305, (15, 18322): 568.6715320609717, (15, 18324): 569.191010281158, (15, 18325): 571.5324484887432, (15, 18326): 570.6560566614218, (15, 18327): 567.749683308822, (15, 18329): 572.4882597727893, (15, 18330): 571.5964826002155, (15, 18331): 569.9815098214734, (15, 18332): 568.3672047698009, (15, 18333): 571.2685456449664, (15, 18336): 569.8216058504327, (15, 18337): 570.5630507656851, (15, 18403): 569.9063180019335, (15, 18432): 542.3120265519834, (15, 18451): 560.7498430903335, (15, 18466): 579.629622528769, (15, 18481): 567.0853433480052, (15, 18483): 567.1393880800417, (15, 18484): 565.8107489753407, (15, 18485): 561.7741129793618, (15, 18486): 565.0569227158968, (15, 18487): 562.0251155462703, (15, 18489): 564.8523954236695, (15, 18490): 567.7064777929363, (15, 18491): 569.1116106119772, (15, 18492): 559.0587206542599, (15, 18493): 564.5084218344836, (15, 18494): 564.3208710118856, (15, 18495): 566.6528522559441, (15, 18496): 565.2168518327128, (15, 18497): 561.2931143885969, (15, 18498): 562.1443481614201, (15, 18499): 564.3505552030274, (15, 18501): 562.6760531324675, (15, 18502): 561.2620121308313, (15, 18503): 560.2278788162116, (15, 18504): 565.8565053638953, (15, 18506): 562.7725538781685, (15, 18507): 561.4075557718489, (15, 18508): 563.9987716893813, (15, 18509): 563.9852163834104, (15, 18510): 560.2061119605027, (15, 18511): 564.8533267392748, (15, 18512): 563.2649488026225, (15, 18515): 565.9230058943673, (15, 18516): 565.8925441152389, (15, 18517): 564.0563480045557, (15, 18518): 567.0909917400201, (15, 18519): 566.1903298636049, (15, 18520): 563.6368491639532, (15, 18522): 572.3003068773099, (15, 18523): 572.5429630206115, (15, 18532): 574.4131536725426, (15, 18535): 570.4645166015831, (15, 18537): 568.2667863128295, (15, 18539): 568.6930965113858, (15, 18540): 568.9146224946414, (15, 18541): 569.9695102054164, (15, 18542): 570.6455049127103, (15, 18543): 567.2645342137388, (15, 18546): 568.7696643449075, (15, 18555): 572.2162223398751, (15, 18556): 572.8065594470729, (15, 18565): 574.0759115728641, (15, 18567): 574.9715193775429, (15, 18568): 573.1383972482821, (15, 18577): 586.6538092244439, (15, 18583): 584.5367170870622, (15, 18605): 587.578083553228, (15, 18608): 575.9363539849887, (15, 18616): 600.1626239829868, (15, 18618): 610.7965492741345, (15, 18625): 607.5629927908469, (15, 18645): 598.3395731953399, (15, 18646): 600.6164627164472, (15, 18653): 591.2025873085644, (15, 18654): 599.8189836029785, (15, 18655): 594.0661667047001, (15, 18666): 629.6715599780945, (15, 18837): 613.6149369437857, (15, 18974): 564.0021811865615, (15, 18999): 575.0919855027556, (15, 19000): 578.2854910225993, (15, 19174): 455.8975638492997, (15, 19342): 525.0725989660934, (15, 19455): 457.19360619262284, (15, 19555): 333.612396381156, (15, 19564): 362.397679835493, (15, 19573): 352.355912734011, (15, 19586): 346.4593493830762, (15, 19605): 345.05207064878374, (15, 19611): 351.01338567952416, (15, 19614): 342.5600592578185, (15, 19641): 418.25416144237334, (15, 19702): 422.8151388954335, (15, 19713): 416.00148847067, (15, 19731): 282.56924104529395, (15, 19819): 442.49928112568637, (15, 19893): 367.78237439319525, (15, 19899): 416.230076438291, (15, 19929): 374.72901179982017, (15, 19951): 451.9102681353961, (15, 19962): 391.8812276512294, (15, 19970): 386.8774845176316, (15, 19971): 392.13525734861247, (15, 19972): 389.3135177635687, (15, 19975): 382.78970449113706, (15, 19978): 447.7515395211033, (15, 19987): 446.1549098786521, (15, 19989): 424.5793872399076, (15, 20039): 448.71411532098784, (15, 20043): 453.79584096736176, (15, 20047): 443.3864327321097, (15, 20052): 422.6184263099561, (15, 20054): 426.40663835336676, (15, 20085): 511.2016449456073, (15, 20104): 517.3474352767136, (15, 20132): 483.4493833260498, (15, 20203): 413.5941397815392, (15, 20280): 422.6388577457152, (15, 20285): 427.86311585469815, (15, 20290): 422.5648814475608, (15, 20297): 415.0559214804459, (15, 20309): 485.53800060004266, (15, 20453): 564.8896222267939, (15, 20485): 370.36591675870926, (15, 20520): 351.34045506813464, (15, 20526): 364.59000178173216, (15, 20698): 981.7227710838624, (15, 20868): 1180.8902568716683, (15, 21042): 9.206520550168852, (15, 21057): 36.38638086517696, (15, 21066): 18.3165229912986, (15, 21075): 6.872768097508522, (15, 21093): 18.32234940500425, (15, 21098): 40.91291478900717, (15, 21127): 12.386264779492793, (15, 21130): 17.1910955822873, (15, 21144): 5.774248772225575, (15, 21146): 13.910427372109675, (15, 21147): 2.884444594678546, (15, 21148): 10.95037552589605, (15, 21153): 40.446740582420695, (15, 21293): 65.45242550207334, (15, 21426): 117.62483840356211, (15, 21442): 167.14622542030185, (15, 21451): 171.6666288530598, (15, 21466): 136.75002890125432, (15, 21469): 139.71190578026386, (15, 21471): 135.5671339499606, (15, 21473): 136.73574655003975, (15, 21475): 134.3972559398, (15, 21482): 145.36263165802103, (15, 21484): 142.7753823472162, (15, 21488): 141.9861093463416, (15, 21494): 129.08232140370026, (15, 21498): 132.63639742402896, (15, 21500): 122.89929029060909, (15, 21514): 114.43564949949312, (15, 21537): 110.59203209255088, (15, 21662): 109.0230164958155, (15, 21691): 87.41748362287916, (15, 21757): 107.81884545716541, (15, 21777): 109.21587570994883, (15, 21778): 114.99561025767197, (15, 21779): 115.16956134938911, (15, 21790): 99.13057378567524, (15, 21802): 106.3565454817101, (15, 21824): 104.84433354066107, (15, 21874): 118.2575378120816, (15, 21879): 128.5883687653197, (15, 21983): 71.41965663204418, (15, 22002): 62.87700298955079, (15, 22132): 86.097797007065, (15, 22261): 1017.3184962313285, (15, 22298): 1006.232056822313, (15, 22339): 1093.1769492702683, (15, 22508): 883.3711269761824, (15, 22841): 2396.5447536832708, (15, 22842): 2396.6746103043906, (15, 22874): 2380.5080911287578, (15, 22941): 2381.8690753304477, (15, 22956): 2392.0293544810347, (15, 22960): 2394.7697919029342, (15, 22968): 2405.9818633364357, (15, 22970): 2408.569435712563, (15, 22974): 2414.2953557538613, (15, 22980): 2426.407688234743, (15, 23025): 2426.20171670218, (15, 23028): 2423.697622432257, (15, 23081): 2445.230943803291, (15, 23104): 2424.8822935566686, (15, 23147): 2315.2722354415564, (15, 23298): 208.1405118450959, (15, 23376): 188.50175753993346, (15, 23381): 172.34536732719883, (15, 23529): 216.79558771135171, (15, 23556): 205.87046479894465, (15, 23718): 202.65498903385904, (15, 24001): 325.6099592522533, (15, 24094): 355.19982634954164, (15, 24129): 374.63590464316235, (15, 24174): 333.56591198138614, (15, 24235): 376.4569039324389, (15, 24259): 394.9857355784554, (15, 24260): 393.5563266030077, (15, 24261): 389.44739435139377, (15, 24305): 417.2568456356496, (15, 24306): 420.8973187693195, (15, 24307): 415.31353558866664, (15, 24308): 381.53685985926813, (15, 24498): 469.5448253346551, (15, 24499): 469.85482441966684, (15, 24500): 466.38838600897714, (15, 24668): 450.66156172211276, (15, 24711): 491.70115210078177, (15, 24756): 503.83568875720067, (15, 24788): 509.6542545057967, (15, 24809): 487.7197773758462, (15, 24813): 494.5084964228713, (15, 24821): 492.2697136581498, (15, 24825): 493.9143090687222, (15, 24832): 486.2437852175304, (15, 24833): 489.55210955259423, (15, 24835): 492.85111078508015, (15, 24837): 498.12897667651987, (15, 24840): 485.7394470846811, (15, 24841): 490.84253103805315, (15, 24844): 485.90397253712877, (15, 24845): 488.89207868470555, (15, 24846): 488.6522822685485, (15, 24849): 490.45892509748097, (15, 24850): 495.513589201407, (15, 24863): 449.431056664127, (15, 24866): 455.3381092366436, (15, 24885): 462.37784059191506, (15, 24886): 462.92722842373024, (15, 24889): 475.9221365709246, (15, 24903): 481.09682315285687, (15, 24909): 459.472618079874, (15, 24999): 728.7477309759233, (15, 25019): 723.6513311528306, (15, 25028): 724.6315030087796, (15, 25137): 505.5546387674554, (15, 25145): 508.2394940918425, (15, 25208): 607.9056377933355, (15, 25233): 605.371574259696, (15, 25371): 462.43967985789607, (15, 25377): 440.4709835399401, (15, 25828): 404.24622272261826, (15, 25851): 402.0549440620546, (15, 25874): 384.4368627747459, (15, 25898): 405.2478940883739, (15, 25946): 404.76099028731556, (15, 26047): 435.6080591273783, (15, 26066): 290.8232323832511, (15, 26197): 352.9732001776955, (15, 26212): 593.494028655327, (15, 26253): 613.442820824922, (15, 26254): 603.9083998933752, (15, 26257): 603.1180286005174, (15, 26258): 611.2069564169359, (15, 26260): 606.5761591161387, (15, 26266): 600.266986362426, (15, 26267): 596.8583300199411, (15, 26271): 598.385786124528, (15, 26304): 522.3711670285041, (15, 26305): 518.321076282442, (15, 26363): 448.28627153522865, (15, 26441): 1076.570622681403, (15, 26442): 1074.1330202602242, (15, 26450): 1063.4538293225633, (15, 26459): 1063.6442806147732, (15, 26462): 1065.6064807629834, (15, 26467): 1097.0819899649102, (15, 26471): 1087.7317313559136, (15, 26472): 1086.6453240260353, (15, 26473): 1086.1376815098688, (15, 26476): 1079.6591985634543, (15, 26485): 1068.4715134140909, (15, 26493): 1068.2808005773436, (15, 26524): 1070.8091187128732, (15, 26525): 1069.2780607695947, (15, 26556): 1083.522821212717, (15, 26560): 1083.3609626368157, (15, 26561): 1076.7709559176585, (15, 26564): 1080.3834662697595, (15, 26569): 1074.8177407943645, (15, 26570): 1071.7715181857036, (15, 26573): 1073.0456475780322, (15, 26581): 1072.4110034062844, (15, 26583): 1070.2987884619279, (15, 26593): 1072.010295537967, (15, 26837): 1098.824340772082, (15, 26844): 1106.1975470512334, (15, 26863): 1089.2453160005246, (15, 26893): 1110.0969842472791, (15, 26902): 1120.0725095042114, (15, 26905): 1110.7644508059072, (15, 26912): 1118.2976871787225, (15, 26921): 1099.286874895769, (15, 26922): 1078.1168805065965, (15, 27212): 1174.544174408692, (15, 27218): 1167.1613183698248, (15, 27239): 1188.2546224931796, (15, 27257): 1180.4793256014946, (15, 27274): 1190.8222266366904, (15, 27279): 1188.7214792921618, (15, 27282): 1180.5048388291395, (15, 27283): 1184.8000848846928, (15, 27285): 1194.2204114416245, (15, 27286): 1185.7562008814004, (15, 27290): 1173.3928526952875, (15, 27295): 1169.142422136706, (15, 27300): 1192.4522999085505, (15, 27344): 1168.033203233867, (15, 27366): 1176.8270248810106, (15, 27383): 1193.8203186994863, (15, 27398): 1205.1448808231762, (15, 27406): 1197.3654494928862, (15, 27407): 1200.2245367142943, (15, 27426): 1193.2179157920446, (15, 27432): 1156.5494120893732, (15, 27460): 1180.0439669939096, (15, 27523): 1171.8803092206028, (15, 27545): 1326.4623558699093, (15, 27602): 1510.1624836992212, (15, 27606): 1514.0737057610243, (15, 27646): 1311.2540580343934, (15, 27667): 1348.4144147455984, (15, 27672): 1350.6560524162735, (15, 27674): 1344.1394447706652, (15, 27688): 1350.6136216521274, (15, 27692): 1356.7491794633993, (15, 27693): 1351.1250166554898, (15, 27705): 1350.5029336886962, (15, 27712): 1352.9921661382434, (15, 27786): 1530.8275880381404, (15, 27790): 1514.372400090369, (15, 27791): 1513.2772107411793, (15, 27795): 1520.0190930377794, (15, 27801): 1507.3237250103418, (15, 27813): 1536.0606786064423, (15, 27816): 1530.1464607335906, (15, 27823): 1506.8858552031613, (15, 27830): 1522.947817523638, (15, 27884): 1245.8106745818477, (15, 27885): 1295.121267605845, (15, 27896): 1265.4884444459276, (15, 27919): 1263.7706954457099, (15, 27922): 1269.4299335914166, (15, 27930): 1253.7169512507246, (15, 27934): 1255.3194097467174, (15, 27935): 1256.3881884307086, (15, 27948): 1477.4156457328615, (15, 27951): 1491.8930388737251, (15, 28061): 1279.3788690207273, (15, 28290): 1676.919633853013, (15, 28292): 1683.9989063547284, (15, 28293): 1678.2133691211561, (15, 28295): 1674.1402975116573, (15, 28296): 1676.1518854891542, (15, 28297): 1673.0922839669217, (15, 28302): 1669.6119677618883, (15, 28310): 1782.17063067174, (15, 28313): 1788.0559323359273, (15, 28372): 1789.696680507559, (15, 28398): 1790.2912299626544, (15, 28399): 1787.6493300107688, (15, 28400): 1791.8591611043773, (15, 28401): 1780.8835551545267, (15, 28445): 1784.0401982112483, (15, 28475): 1772.8636689754755, (15, 28885): 379.4210879341451, (15, 28886): 376.2544138050334, (15, 28915): 381.030717968666, (15, 28916): 377.4633968001661, (15, 28917): 375.9682664026441, (15, 28921): 385.7269037133095, (15, 28931): 385.12252080503663, (15, 28945): 375.1051731142175, (15, 28982): 376.2949264293539, (15, 29219): 413.54910097097616, (15, 29228): 397.65595728280283, (15, 29246): 512.2776018663307, (15, 29248): 515.5661329725576, (15, 29282): 492.70780761621387, (15, 29290): 518.4711744770213, (15, 29291): 515.2609087690638, (15, 29292): 518.8761545668589, (15, 29293): 510.1411080393625, (15, 29294): 518.9288512364526, (15, 29298): 511.94491700415335, (15, 29299): 512.3800313292114, (15, 29304): 501.6399760197573, (15, 29317): 479.19444906105304, (15, 29323): 477.32463376801877, (15, 29330): 488.331803483257, (15, 29331): 492.8497848680041, (15, 29344): 424.66365058388834, (15, 29445): 286.47785737456235, (15, 29724): 2360.8800160050664, (15, 29738): 2364.123430184694, (15, 29745): 2354.3552564764273, (15, 29748): 2354.6817015293095, (15, 29750): 2359.337578475978, (15, 29759): 2350.423155001384, (15, 29772): 2362.38627990934, (15, 29781): 2359.7303463495314, (15, 29784): 2358.342060550771, (15, 29790): 2362.0648337718067, (15, 29811): 2354.576587761601, (15, 29817): 2372.7654896932977, (15, 29818): 2370.1561684549038, (15, 29929): 2354.189410922405, (15, 30039): 2400.7826731742794, (15, 30066): 2375.986739454471, (15, 30116): 2262.2734984077433, (15, 30238): 2094.1071774375764, (15, 30248): 2181.181857451742, (15, 30260): 2183.4467273931523, (15, 30545): 320.49910285304884, (15, 30733): 145.19624110618727, (15, 30756): 115.16199479598795, (15, 30921): 186.3891186103869, (15, 31079): 411.74345881109645, (15, 31149): 382.04138578103215, (15, 31154): 388.4426712241267, (15, 31160): 381.9418682623182, (15, 31163): 389.9201506642871, (15, 31189): 421.85756072531285, (15, 31215): 424.74764109241323, (15, 31259): 456.5251564456791, (15, 31262): 458.6425100762161, (15, 31430): 431.7537696723732, (15, 31568): 580.8376604886996, (15, 31751): 444.0960378118487, (16, 109): 692.1754479449206, (16, 872): 1037.5858517450897, (16, 873): 1046.0691934969323, (16, 877): 1044.498522319268, (16, 879): 1045.913825620856, (16, 884): 1041.0345385224296, (16, 889): 1045.5688163402538, (16, 891): 1037.7934699804123, (16, 892): 1052.1547330717988, (16, 894): 1050.4242100758865, (16, 896): 1039.58261928557, (16, 903): 1046.666353139359, (16, 909): 1026.9319439491003, (16, 910): 1028.8420122340794, (16, 912): 1023.5813804203382, (16, 913): 1018.3364123512072, (16, 916): 1013.9401165981576, (16, 926): 1029.682022973576, (16, 927): 1026.5034227501517, (16, 948): 1034.4601456359474, (16, 961): 1032.8427130010068, (16, 962): 1032.7686870923224, (16, 963): 1033.022374778364, (16, 967): 1049.592227513513, (16, 974): 1048.8454806491272, (16, 998): 1054.280262907829, (16, 1014): 1221.5814902039183, (16, 1086): 975.6026696319054, (16, 1087): 969.8216613745095, (16, 1089): 964.4520046079583, (16, 1090): 968.4146759328219, (16, 1092): 980.6535304263657, (16, 1097): 972.2516312175654, (16, 1107): 983.7861593080885, (16, 1387): 351.6892414446393, (16, 1554): 479.32252024331615, (16, 1827): 1459.447367136192, (16, 1828): 1459.6336439985132, (16, 1829): 1461.4316662638282, (16, 1830): 1463.4712882581534, (16, 1831): 1463.6306209295333, (16, 1832): 1462.3842145333206, (16, 1833): 1461.904818514252, (16, 1836): 1460.2664600872818, (16, 1841): 1466.58875135699, (16, 1843): 1464.2980212962666, (16, 1844): 1465.895431095424, (16, 1845): 1463.6766885810603, (16, 1847): 1453.1401655799875, (16, 1848): 1456.3899309903761, (16, 1849): 1472.19649485712, (16, 1850): 1473.254178778967, (16, 1851): 1460.4267761288777, (16, 1852): 1462.007817798767, (16, 1854): 1462.4980167854142, (16, 1856): 1454.459215563974, (16, 1857): 1456.90196008471, (16, 1858): 1469.785807736342, (16, 1861): 1462.3816962607111, (16, 1866): 1455.4190635094526, (16, 1867): 1465.6153185177873, (16, 1868): 1462.6811476978676, (16, 1870): 1467.3770835169844, (16, 1871): 1464.072927702905, (16, 1875): 1461.4258549829303, (16, 1880): 1455.2679555641557, (16, 1882): 1458.1377718716437, (16, 1883): 1471.8522239544884, (16, 1889): 1454.6862041972513, (16, 1893): 1459.4186986256113, (16, 1894): 1456.849815059076, (16, 1899): 1451.839301718619, (16, 1900): 1452.9953206799926, (16, 1902): 1463.216033028148, (16, 1905): 1466.9116684843048, (16, 1907): 1457.1478370287275, (16, 1910): 1456.5348925570065, (16, 1917): 1468.5125585629187, (16, 1920): 1456.1792582536907, (16, 1935): 1464.7361031816022, (16, 1937): 1467.5770812361109, (16, 1946): 1443.961454098793, (16, 1949): 1445.9267084938976, (16, 1950): 1440.0187995258202, (16, 1951): 1443.6030401265066, (16, 1952): 1450.418577394851, (16, 1953): 1448.6628091302607, (16, 1954): 1448.9062779910125, (16, 1958): 1446.6168186994882, (16, 1960): 1451.952602083873, (16, 1968): 1454.0503365287261, (16, 1969): 1462.7073600757956, (16, 1974): 1460.6713187145933, (16, 1975): 1461.5037939473416, (16, 1979): 1453.5556929770296, (16, 1980): 1455.6645536144356, (16, 1981): 1455.8499499874722, (16, 1985): 1456.6288823721798, (16, 1994): 1442.5216095777653, (16, 2011): 1458.927565292013, (16, 2019): 1484.553547979357, (16, 2020): 1481.1849353243783, (16, 2029): 1470.97901984482, (16, 2030): 1478.8084823023703, (16, 2032): 1470.6523573508953, (16, 2033): 1474.7607890963832, (16, 2034): 1475.9730697195962, (16, 2036): 1470.8030260686508, (16, 2037): 1471.9072073082266, (16, 2038): 1466.6596894473753, (16, 2042): 1501.3179928759403, (16, 2050): 1471.3002899480764, (16, 2051): 1472.2087269003139, (16, 2053): 1472.5095564606268, (16, 2054): 1475.6235170974346, (16, 2066): 1469.534699373516, (16, 2067): 1468.8334148800593, (16, 2071): 1436.0613364163985, (16, 2072): 1440.6782062796894, (16, 2073): 1421.5724999968982, (16, 2074): 1421.6964376539665, (16, 2080): 1414.422004873333, (16, 2082): 1443.4838588540533, (16, 2083): 1445.7888128223262, (16, 2089): 1438.6583672754552, (16, 2090): 1440.5726398176303, (16, 2092): 1436.1233125503777, (16, 2098): 1416.2471235487633, (16, 2099): 1420.3274306618594, (16, 2101): 1416.8908314015025, (16, 2102): 1430.4753140274029, (16, 2103): 1426.7030833165538, (16, 2104): 1425.2255634247485, (16, 2106): 1448.278497020017, (16, 2112): 1419.848903540983, (16, 2113): 1433.1685076795975, (16, 2114): 1438.5811454143309, (16, 2117): 1451.419009369949, (16, 2123): 1383.745994446725, (16, 2124): 1386.5853681139506, (16, 2134): 1381.542652201581, (16, 2138): 1388.669262785374, (16, 2141): 1381.5859029852036, (16, 2148): 1397.698498603838, (16, 2150): 1375.2522399782054, (16, 2151): 1379.1066831521914, (16, 2152): 1374.495105927254, (16, 2153): 1397.4994481614654, (16, 2154): 1385.0261994762539, (16, 2155): 1385.7323258676993, (16, 2156): 1382.0829589787313, (16, 2157): 1392.598552310423, (16, 2160): 1398.3434634818914, (16, 2161): 1375.1893751575521, (16, 2162): 1402.5964161159059, (16, 2163): 1398.2179042790888, (16, 2164): 1398.6948791610714, (16, 2168): 1382.5295848645433, (16, 2172): 1390.7185765479803, (16, 2174): 1380.2618887527576, (16, 2178): 1394.6758492461595, (16, 2179): 1393.3109774560585, (16, 2183): 1389.8412520003594, (16, 2185): 1390.7515924231518, (16, 2186): 1388.0987046754615, (16, 2190): 1397.5979617246671, (16, 2192): 1393.074457482368, (16, 2193): 1390.228350017148, (16, 2194): 1385.6120796443374, (16, 2195): 1386.5144671927394, (16, 2197): 1394.8366167908366, (16, 2205): 1390.6187229451548, (16, 2207): 1384.650433322738, (16, 2208): 1388.3037264226143, (16, 2212): 1388.1577565309626, (16, 2214): 1324.2257910051453, (16, 2225): 1339.5283294078288, (16, 2231): 1284.0455710781814, (16, 2278): 1394.3952642801964, (16, 2284): 1406.2818417047804, (16, 2285): 1406.1274706099744, (16, 2291): 1395.5580526346423, (16, 2292): 1388.4453515908344, (16, 2307): 1400.5661253092258, (16, 2313): 1396.2840471877885, (16, 2317): 1378.0585455957214, (16, 2319): 1392.479048682325, (16, 2321): 1398.1699970246718, (16, 2323): 1395.0790478634894, (16, 2326): 1406.430646883877, (16, 2327): 1402.4466679070408, (16, 2329): 1399.9862724613486, (16, 2330): 1397.7763252558843, (16, 2332): 1405.5148100688625, (16, 2344): 1391.752320605142, (16, 2346): 1393.3161575247009, (16, 2361): 1377.3213803948795, (16, 2368): 1432.1349920187283, (16, 2374): 1437.8634387856257, (16, 2375): 1438.4800833904617, (16, 2377): 1421.8011112212832, (16, 2378): 1441.9974496485067, (16, 2379): 1444.1159316158519, (16, 2380): 1444.416952958084, (16, 2383): 1424.8764948176774, (16, 2385): 1426.6653480142134, (16, 2395): 1425.4100728924625, (16, 2397): 1443.0575013175257, (16, 2398): 1416.6789052822216, (16, 2399): 1421.4752811987262, (16, 2400): 1420.184839278051, (16, 2402): 1433.895259664324, (16, 2403): 1437.4966309764175, (16, 2404): 1437.7156950213434, (16, 2405): 1429.6742975097768, (16, 2407): 1435.1988410981307, (16, 2408): 1440.1585426870358, (16, 2409): 1431.8427124068944, (16, 2411): 1440.355277511191, (16, 2412): 1438.3271075879065, (16, 2413): 1441.6768616119064, (16, 2414): 1437.2688544949003, (16, 2422): 1440.269473584631, (16, 2424): 1438.7102218221767, (16, 2426): 1438.9035282032014, (16, 2433): 1433.3470878388136, (16, 2436): 1433.4654591017184, (16, 2437): 1412.0389755803565, (16, 2440): 1416.2427309566135, (16, 2445): 1524.2326698140373, (16, 2447): 1511.2409094798084, (16, 2454): 1521.85181985027, (16, 2455): 1521.0447318744668, (16, 2460): 1489.9688017636709, (16, 2461): 1494.1092947652505, (16, 2471): 1567.4638241864095, (16, 2492): 1555.7131421714537, (16, 2511): 1513.6480734777842, (16, 2523): 1535.3722196844622, (16, 2525): 1533.759201584268, (16, 2535): 1511.183359205235, (16, 2537): 1505.0151243431064, (16, 2538): 1507.812361348607, (16, 2539): 1512.975962870052, (16, 2540): 1514.16682095582, (16, 2542): 1521.1520334070865, (16, 2559): 1605.2518442105734, (16, 2575): 1604.61345766922, (16, 2599): 1435.4941194209666, (16, 2600): 1473.6127140722924, (16, 2607): 1446.203328380649, (16, 2627): 1559.895018698047, (16, 2647): 1583.5954991800263, (16, 2674): 1565.8536608333584, (16, 2681): 1567.2596191598782, (16, 2683): 1574.507677562614, (16, 2686): 1562.1911628604942, (16, 2689): 1686.7824809344045, (16, 2690): 1688.3173491929538, (16, 2713): 1740.3657746775532, (16, 2714): 1746.3479854136897, (16, 2715): 1749.1213666721856, (16, 2739): 1745.495953739463, (16, 2740): 1716.990810047638, (16, 2741): 1717.5997991708757, (16, 2749): 1745.8308869542777, (16, 2750): 1745.2935160727409, (16, 2752): 1746.6364575834089, (16, 2755): 1749.7243611860556, (16, 2758): 1750.2647331705368, (16, 2759): 1749.6419480572981, (16, 2769): 1744.8040416249264, (16, 2771): 1724.347062186351, (16, 2779): 1735.438130940676, (16, 2784): 1708.356100578187, (16, 2800): 1724.2467622255272, (16, 2802): 1716.9998636791408, (16, 2803): 1714.6514743564007, (16, 2804): 1712.2647083498014, (16, 2805): 1723.237896067809, (16, 2807): 1721.763597927325, (16, 2809): 1723.6164127483073, (16, 2812): 1702.2537985061851, (16, 2814): 1731.3034872732003, (16, 2817): 1743.6794159018557, (16, 2819): 1718.9587143452725, (16, 2823): 1715.304486628013, (16, 2832): 1728.5783097337965, (16, 2836): 1715.6994171153792, (16, 2839): 1720.4073404834596, (16, 2841): 1738.3366542650476, (16, 2843): 1735.2848918466325, (16, 2846): 1723.5019482602715, (16, 2849): 1732.7806003023982, (16, 2852): 1729.0241500014504, (16, 2853): 1734.5898027226453, (16, 2876): 1741.9621088642186, (16, 2877): 1753.1806421963624, (16, 2885): 1768.7204784925393, (16, 2918): 1712.1721843770142, (16, 2921): 1718.1789616273854, (16, 2925): 1685.8546281564038, (16, 2926): 1672.7110742449931, (16, 2930): 1709.0314827328982, (16, 2931): 1691.321001050693, (16, 2938): 1714.4663924373635, (16, 2940): 1717.0167354870546, (16, 2947): 1698.867125523716, (16, 2949): 1703.8239671525441, (16, 2950): 1708.0448452898522, (16, 2952): 1705.8914363530605, (16, 2958): 1704.5507634736705, (16, 2959): 1704.1407594662942, (16, 2960): 1709.9385343544095, (16, 2961): 1708.5718247402451, (16, 2963): 1703.9500711116573, (16, 2968): 1706.6748245280153, (16, 2976): 1702.0200013733845, (16, 2981): 1676.293006309881, (16, 2982): 1677.7971595882273, (16, 2984): 1676.2764325637247, (16, 3003): 1675.5097414095378, (16, 3046): 1616.8139204321474, (16, 3050): 1653.3415263427687, (16, 3051): 1654.0203059345768, (16, 3053): 1650.4109236336822, (16, 3069): 1681.2973796250158, (16, 3071): 1643.1636221800482, (16, 3080): 1773.2860147591782, (16, 3199): 1685.2164004017147, (16, 3200): 1682.1982180713176, (16, 3205): 1710.7002722605805, (16, 3209): 1685.0543483269378, (16, 3215): 1680.9788646772681, (16, 3217): 1675.4043034819522, (16, 3249): 1679.8890871810293, (16, 3263): 1721.4885695929852, (16, 3289): 1688.9415424524075, (16, 3301): 1694.2103103986249, (16, 3302): 1690.7477499490399, (16, 3307): 1687.8196911029045, (16, 3310): 1696.6227528590352, (16, 3391): 1778.7516361239987, (16, 3509): 774.6972744212045, (16, 3510): 771.7380211536569, (16, 3511): 770.8763726054649, (16, 3512): 766.5638384337269, (16, 3514): 764.9419917519099, (16, 3519): 795.4844512913887, (16, 3536): 774.9912750414314, (16, 3545): 776.8795372187132, (16, 3548): 768.568038370205, (16, 3572): 780.1188244944422, (16, 3581): 785.9011484645101, (16, 3583): 772.2519151783407, (16, 3601): 805.4684684389819, (16, 3656): 811.3985411043476, (16, 3669): 829.0163260905553, (16, 3670): 832.626117711753, (16, 3695): 808.0006775408991, (16, 3696): 809.6155105896732, (16, 3782): 720.9987044000299, (16, 3792): 725.0224024203435, (16, 3989): 1701.7516714109613, (16, 4008): 1727.7119270286266, (16, 4031): 1730.4981392278937, (16, 4045): 1717.0263433292046, (16, 4144): 1714.215483027576, (16, 4145): 1683.5114486953119, (16, 4164): 1703.097479941292, (16, 4168): 1692.8321364964665, (16, 4173): 1690.0952721289273, (16, 4181): 1674.2734642429705, (16, 4228): 1664.2182628584924, (16, 4248): 1651.0791392979215, (16, 4254): 1486.9733624668638, (16, 4260): 1489.9042076135822, (16, 4262): 1497.5811506781574, (16, 4273): 1497.1086443091117, (16, 4319): 1396.211619159925, (16, 4326): 1393.864705545657, (16, 4328): 1395.7436266830284, (16, 4334): 1399.2596211925957, (16, 4335): 1396.6400551737875, (16, 4372): 1065.5492142157377, (16, 4413): 1129.5577541301857, (16, 4434): 1064.5048416674758, (16, 4447): 1079.3734221588093, (16, 4452): 1064.57592111258, (16, 4463): 884.9148305253498, (16, 4465): 892.0474107055547, (16, 4619): 1121.6779147006798, (16, 4645): 1141.5042924199101, (16, 4657): 1136.754751636735, (16, 4666): 1128.217224308097, (16, 4676): 1140.4146496901342, (16, 4678): 1144.0791695079968, (16, 4689): 1133.405762205973, (16, 4704): 1193.6520419131823, (16, 4726): 1300.8783700079653, (16, 4727): 1298.6548887626357, (16, 4730): 1294.472468975512, (16, 4731): 1294.8571854822812, (16, 4734): 1301.9762695336012, (16, 4735): 1299.168192417851, (16, 4736): 1299.6065037008266, (16, 4737): 1295.0463260759707, (16, 4738): 1295.0445937425973, (16, 4756): 1296.8833143605216, (16, 4760): 1289.328546242559, (16, 4761): 1292.0142290757626, (16, 4762): 1285.4514499735324, (16, 4765): 1289.980970953845, (16, 4773): 1305.938263129713, (16, 4774): 1302.7621850587523, (16, 4790): 1304.6375383531154, (16, 4795): 1302.9944687495831, (16, 4799): 1303.0997991562413, (16, 4801): 1306.180436472642, (16, 4804): 1305.2533577984889, (16, 4805): 1303.8924292363124, (16, 4806): 1300.1725033998214, (16, 4815): 1296.9964480563215, (16, 4816): 1303.13349841535, (16, 4817): 1302.9041246020531, (16, 4826): 1299.9711811739303, (16, 4830): 1296.2160658245766, (16, 4839): 1295.6653213893455, (16, 4840): 1297.0268745757544, (16, 4841): 1291.8881353225167, (16, 4846): 1290.6008572033866, (16, 4848): 1288.8781580182442, (16, 4850): 1290.6755555181628, (16, 4871): 1271.0406176502656, (16, 4883): 1288.6651230718082, (16, 4900): 1281.3579326834288, (16, 4901): 1277.6367988121322, (16, 4917): 1093.0688748117418, (16, 4931): 1075.9118114266548, (16, 4944): 1096.0349701941948, (16, 4956): 1078.0255023407708, (16, 4958): 1075.50911163616, (16, 4959): 1070.8687042652302, (16, 4961): 1082.3270250984033, (16, 4966): 1072.65828831687, (16, 5207): 1053.481252196, (16, 5272): 856.249826805297, (16, 5283): 859.560313524955, (16, 5287): 856.7437910873559, (16, 5289): 857.9759921020726, (16, 5293): 865.157058231156, (16, 5295): 875.5938050385013, (16, 5296): 870.4499389683695, (16, 5298): 867.5093350337552, (16, 5303): 866.4404944506126, (16, 5305): 844.1228310985545, (16, 5306): 833.9603695880897, (16, 5307): 841.7571723356658, (16, 5308): 844.1794510410067, (16, 5313): 850.4737016916025, (16, 5314): 854.7566567604897, (16, 5317): 840.8847622201268, (16, 5319): 861.4728724764599, (16, 5324): 863.1439572061743, (16, 5326): 864.553241762557, (16, 5348): 828.693979973202, (16, 5351): 824.435328037662, (16, 5399): 853.0102825821737, (16, 5413): 818.5122497481616, (16, 5422): 860.0547799884461, (16, 5445): 848.7471023107569, (16, 5448): 844.9280754598227, (16, 5456): 838.7177474247525, (16, 5467): 840.8957799485327, (16, 5624): 819.3104188356648, (16, 5671): 1008.4094256328855, (16, 5672): 1003.4864325664311, (16, 5797): 1075.6481677170907, (16, 5871): 872.3214644862583, (16, 5976): 816.1710838375534, (16, 6118): 1384.67062837847, (16, 6248): 1527.3084856201356, (16, 6345): 948.8377980483488, (16, 6352): 943.2317142157434, (16, 6354): 948.2271463631071, (16, 6359): 953.0598620250828, (16, 6376): 953.2037487899156, (16, 6378): 947.9400044466336, (16, 6381): 955.1121315145455, (16, 6383): 946.1359002004574, (16, 6396): 969.0107205912628, (16, 6399): 953.3458343515836, (16, 6408): 939.69476414718, (16, 6409): 932.56615081556, (16, 6419): 908.1111331357018, (16, 6422): 932.693980914514, (16, 6423): 931.6920318441316, (16, 6424): 936.7937994945307, (16, 6439): 932.5056896652707, (16, 6464): 927.7943992158073, (16, 6465): 930.5172788201818, (16, 6469): 938.3068372202714, (16, 6470): 939.5753697550614, (16, 6472): 956.5465814697204, (16, 6480): 939.3339222060663, (16, 6486): 926.6794330056964, (16, 6497): 930.0478418964472, (16, 6503): 908.9053825966236, (16, 6508): 919.762996772467, (16, 6509): 916.2855326276001, (16, 6521): 933.0524743231379, (16, 6544): 922.7397697134425, (16, 6552): 916.4046528401932, (16, 6553): 914.3914891314122, (16, 6554): 912.4856242828776, (16, 6578): 921.2462121780369, (16, 6582): 909.5053579742196, (16, 6601): 919.9353205390647, (16, 6609): 944.925356438278, (16, 6610): 943.2462501829928, (16, 6611): 949.2097333689651, (16, 6614): 951.6858300210047, (16, 6615): 950.0347587107949, (16, 6616): 944.5182675424155, (16, 6617): 946.3003320899418, (16, 6618): 941.4694202581261, (16, 6619): 949.324515442012, (16, 6620): 941.0728918719535, (16, 6621): 938.9008417028559, (16, 6622): 941.6566715582442, (16, 6623): 947.7124260414384, (16, 6624): 942.7678786660293, (16, 6625): 944.3870783966913, (16, 6626): 950.7768998847807, (16, 6627): 954.3980761835968, (16, 6628): 937.2247095676618, (16, 6629): 938.8726620527675, (16, 6630): 948.7871604341522, (16, 6632): 940.6664071864544, (16, 6634): 945.0055941313921, (16, 6635): 940.2632336450059, (16, 6636): 943.3935044934489, (16, 6637): 936.5030942615582, (16, 6638): 945.6174108789891, (16, 6639): 952.4995544543698, (16, 6640): 947.6322304682438, (16, 6641): 936.1345093736894, (16, 6642): 943.313579805079, (16, 6643): 953.11589205662, (16, 6645): 947.9308603443751, (16, 6646): 943.6779498462951, (16, 6647): 945.0410295192063, (16, 6653): 951.0479773719835, (16, 6655): 953.6543877446754, (16, 6658): 943.5255062104129, (16, 6662): 940.7229671128664, (16, 6819): 818.2584168384179, (16, 6996): 787.9084752676623, (16, 7059): 809.6156250389824, (16, 7187): 657.7781749978404, (16, 7304): 681.7113267062247, (16, 7528): 735.8453181893132, (16, 7720): 920.698513401496, (16, 7793): 901.4943947116898, (16, 7807): 908.8649386306977, (16, 7808): 897.0512045978567, (16, 7831): 932.2197437400935, (16, 7850): 970.1443865979355, (16, 7852): 969.9605584043328, (16, 8012): 936.146565214947, (16, 8125): 854.2596248696585, (16, 8208): 968.5087712156197, (16, 8392): 897.5140804445497, (16, 8651): 748.4769535560173, (16, 9088): 887.5096194028981, (16, 9443): 512.7388766252186, (16, 9444): 510.7968283964692, (16, 9828): 402.306478184519, (16, 9868): 495.2209122580059, (16, 10180): 850.8166394602331, (16, 10256): 923.8716183688592, (16, 10276): 900.3463918858886, (16, 10378): 946.5292741332221, (16, 10676): 771.5295949579712, (16, 10714): 705.9467367762443, (16, 10730): 756.2500567525052, (16, 10862): 511.2231326694171, (16, 10881): 526.7166885324972, (16, 10883): 524.7566115177835, (16, 10885): 507.9562368289937, (16, 10891): 521.7453982603038, (16, 10909): 520.9455387229784, (16, 10911): 523.7452699930208, (16, 10913): 519.9632365725023, (16, 10915): 520.1384838595956, (16, 10919): 522.584482768238, (16, 11037): 413.923370644061, (16, 11039): 374.99376557277856, (16, 11516): 2016.4851177949645, (16, 11856): 1401.4307139589039, (16, 11857): 1393.7817255852674, (16, 11861): 1397.6369029136827, (16, 11881): 1399.2744233383887, (16, 11902): 1383.6696673112197, (16, 11911): 1385.0941910002973, (16, 11914): 1385.4023229324011, (16, 11922): 1395.5177570357744, (16, 11924): 1400.2813513190256, (16, 11926): 1396.0365365280481, (16, 11950): 1409.539740187218, (16, 11963): 1423.5653811629008, (16, 11983): 1421.1638922841357, (16, 11985): 1430.2377714676943, (16, 12009): 1433.7076497953553, (16, 12010): 1422.1833684377546, (16, 12018): 1424.680559656595, (16, 12020): 1426.4871811320022, (16, 12021): 1428.8368376284695, (16, 12024): 1438.4206714952838, (16, 12025): 1433.899187029532, (16, 12027): 1431.9455955327878, (16, 12031): 1420.4724489421574, (16, 12032): 1422.806348293084, (16, 12035): 1434.5170611932117, (16, 12041): 1427.7849715865636, (16, 12045): 1301.8495202745319, (16, 12145): 1369.3604089013215, (16, 12275): 1722.506198759345, (16, 12294): 1703.6397235036543, (16, 12358): 1790.5494425025004, (16, 12463): 1828.8565268695932, (16, 12465): 1828.3419855534414, (16, 12482): 1835.7951997249693, (16, 12503): 1835.4462562435056, (16, 12506): 1838.9995476329505, (16, 12549): 1823.9735784788402, (16, 12559): 1822.7285456979714, (16, 12569): 1828.241942113514, (16, 12572): 1830.7626843392143, (16, 12574): 1824.685564793816, (16, 12576): 1826.175197920775, (16, 12591): 1821.3223965877773, (16, 12608): 1839.7143923934016, (16, 12696): 1802.545543096562, (16, 12710): 1817.06268366255, (16, 12728): 1813.2395458491399, (16, 12766): 1237.6071025818442, (16, 12771): 1191.4484985588806, (16, 12790): 1188.7092116825524, (16, 12795): 1185.0205139643804, (16, 12797): 1138.372442552721, (16, 12798): 1142.2461219746945, (16, 12811): 1170.8696359969704, (16, 12830): 1165.1582262210554, (16, 12848): 1162.2658097536385, (16, 12850): 1159.969181979721, (16, 12852): 1161.442939190905, (16, 12854): 1157.131327021279, (16, 12859): 1164.5227248428282, (16, 12861): 1145.2378020770038, (16, 12865): 1179.6324791339869, (16, 12866): 1175.098680150901, (16, 12867): 1185.8432779941418, (16, 12874): 1180.9529499575874, (16, 12875): 1183.2435733809439, (16, 12881): 1172.4817244948542, (16, 12883): 1177.548367841079, (16, 12885): 1186.6121501846903, (16, 12888): 1173.5493867888622, (16, 12889): 1170.8336920087422, (16, 12892): 1182.7669588754102, (16, 12893): 1175.3352758288697, (16, 12896): 1176.291381539141, (16, 12906): 1188.2993857667943, (16, 13018): 1194.0041270245463, (16, 13071): 1204.3419125272467, (16, 13131): 1132.8466832176427, (16, 13146): 1151.2436135308235, (16, 13159): 1167.0400403583806, (16, 13193): 1124.8222233049316, (16, 13198): 1062.3123780219737, (16, 13292): 1110.2976682387848, (16, 13296): 1108.3996400074466, (16, 13406): 1064.2043189826534, (16, 13407): 1065.207132577246, (16, 13417): 1081.2626090682827, (16, 13418): 1088.9395821236637, (16, 13438): 1092.4822448872178, (16, 13442): 1089.9269378614908, (16, 13443): 1087.1222659538084, (16, 13764): 1017.578676405878, (16, 13766): 1019.266885118066, (16, 13771): 1026.9901977174934, (16, 13783): 1000.5005467224694, (16, 13784): 1017.1141494409932, (16, 13792): 1038.006868792892, (16, 13824): 1001.2355879669443, (16, 14017): 957.612726083022, (16, 14870): 534.4243932695535, (16, 14997): 631.3823927033442, (16, 15000): 627.8658857776608, (16, 15003): 626.6234017233818, (16, 15006): 649.5842855097151, (16, 15007): 651.7892128960095, (16, 15056): 639.8699151952139, (16, 15063): 635.2303910076246, (16, 15069): 630.0074515724718, (16, 15076): 649.4433878964126, (16, 15086): 646.332991808535, (16, 15087): 637.9966823334973, (16, 15111): 634.4188644892295, (16, 15116): 636.0244656289882, (16, 15722): 579.3470369539089, (16, 15998): 425.92034005808415, (16, 16073): 1290.367454765199, (16, 16939): 1253.4920490545194, (16, 16940): 1247.064411642605, (16, 16951): 1259.8469111511536, (16, 16963): 1259.1108029390641, (16, 16965): 1264.5280657965466, (16, 16969): 1266.0642259961855, (16, 16970): 1260.0084763302832, (16, 16971): 1254.9312086101386, (16, 16973): 1256.5673733603624, (16, 16974): 1268.5915339095523, (16, 16976): 1259.158745273123, (16, 16978): 1254.7551872121044, (16, 16980): 1259.3726716194303, (16, 16982): 1270.605136935006, (16, 17045): 1601.4450873284877, (16, 17048): 1609.1624377243259, (16, 17304): 1607.8509283633457, (16, 17305): 1607.2635632233064, (16, 17330): 1610.0542249673995, (16, 17334): 1599.253766446718, (16, 17343): 1616.7305014452652, (16, 17345): 1602.6362544459073, (16, 17347): 1611.8905855018738, (16, 17351): 1588.432186080664, (16, 17372): 1599.7560069098988, (16, 17373): 1615.7036645502235, (16, 17377): 1617.1229136742759, (16, 17382): 1607.5144158622904, (16, 17383): 1608.0719449210073, (16, 17389): 1602.697568674533, (16, 17400): 1611.8787011739762, (16, 17401): 1611.106045896666, (16, 17402): 1612.8003100892035, (16, 17403): 1614.0552233049425, (16, 17440): 1607.1964691853623, (16, 17455): 1617.4624737286335, (16, 17491): 1621.0790399115006, (16, 17507): 1584.9824233389916, (16, 17509): 1589.257595971809, (16, 17590): 1589.0542806063013, (16, 17615): 1536.427233450106, (16, 17642): 1543.5102149215438, (16, 17643): 1544.4777665772156, (16, 17668): 1535.3238149325582, (16, 17721): 1515.0072531221824, (16, 17754): 1561.8767018655112, (16, 17769): 1582.5163126241162, (16, 17776): 1568.5500394787887, (16, 17804): 1590.3053552318902, (16, 17809): 1595.5081294740914, (16, 17824): 1589.7963574549904, (16, 17837): 1585.589325102952, (16, 17838): 1588.2241777503957, (16, 17862): 1585.3558418148814, (16, 17866): 1595.4125780210293, (16, 17872): 1580.376797369242, (16, 17873): 1573.168931580874, (16, 17881): 1584.5394091049388, (16, 17947): 693.4248965820142, (16, 17951): 687.1348065098226, (16, 17953): 683.7267500708787, (16, 17954): 682.7147234145831, (16, 17959): 695.9034968518857, (16, 17963): 697.565286626963, (16, 18000): 661.1148781822193, (16, 18001): 659.11705826894, (16, 18111): 687.883541178596, (16, 18148): 456.9616687757442, (16, 18166): 529.3714854715352, (16, 18189): 626.2948998725428, (16, 18239): 1616.9627920849152, (16, 18240): 1617.2825386047048, (16, 18245): 1617.6470921031735, (16, 18247): 1616.9142764080318, (16, 18251): 1618.0920228360078, (16, 18256): 1619.8131641227872, (16, 18258): 1618.726693888434, (16, 18259): 1619.1675408676865, (16, 18260): 1619.9621967941662, (16, 18262): 1621.1920554004116, (16, 18263): 1620.3731980125685, (16, 18264): 1621.1391538009975, (16, 18266): 1621.9188373039435, (16, 18267): 1622.6145199602015, (16, 18268): 1623.0988857087352, (16, 18269): 1624.5258355663716, (16, 18275): 1623.854346089081, (16, 18285): 1620.7282692933627, (16, 18308): 1605.7312172974043, (16, 18313): 1601.7236668988112, (16, 18314): 1604.746265000688, (16, 18315): 1623.3995453484345, (16, 18316): 1623.804051698381, (16, 18317): 1624.5036216898573, (16, 18320): 1624.4237462100648, (16, 18321): 1625.038470987988, (16, 18322): 1626.0370424316095, (16, 18324): 1626.123604466929, (16, 18325): 1628.521454316542, (16, 18326): 1627.6046383415985, (16, 18327): 1625.5704255307216, (16, 18329): 1629.0294940591234, (16, 18330): 1629.4152978283, (16, 18331): 1627.5602023031288, (16, 18332): 1625.9124243748352, (16, 18333): 1628.7123984644045, (16, 18336): 1626.6047180741732, (16, 18337): 1627.0940161087663, (16, 18403): 1628.7420287279674, (16, 18432): 1610.8445608413915, (16, 18451): 1623.0694917537185, (16, 18466): 1633.491252150352, (16, 18481): 1622.6684234876795, (16, 18483): 1623.0304517415204, (16, 18484): 1621.4323332503875, (16, 18485): 1616.2485479870388, (16, 18486): 1618.4814570102826, (16, 18487): 1614.9639530492702, (16, 18489): 1619.3569267138623, (16, 18490): 1621.426195498241, (16, 18491): 1622.8709918885845, (16, 18492): 1612.1850095126392, (16, 18493): 1617.5280861573979, (16, 18494): 1619.066667940623, (16, 18495): 1620.2944239380734, (16, 18496): 1619.0819015250015, (16, 18497): 1613.8119742332094, (16, 18498): 1616.0194983231875, (16, 18499): 1618.4085483068704, (16, 18501): 1616.027689769577, (16, 18502): 1614.4563344878295, (16, 18503): 1613.7006682173906, (16, 18504): 1620.1337277034982, (16, 18506): 1615.1929951368495, (16, 18507): 1613.4831833647413, (16, 18508): 1617.7180504626422, (16, 18509): 1617.398381211625, (16, 18510): 1613.2228135287294, (16, 18511): 1617.2338324696493, (16, 18512): 1616.1349004185374, (16, 18515): 1619.7548560424552, (16, 18516): 1618.6602117879052, (16, 18517): 1616.1448158691996, (16, 18518): 1620.2431469984963, (16, 18519): 1620.6753548046906, (16, 18520): 1617.7083622683454, (16, 18522): 1627.8328864302703, (16, 18523): 1627.7526151607658, (16, 18532): 1629.2492422443904, (16, 18535): 1625.7268036502635, (16, 18537): 1623.7657526642683, (16, 18539): 1623.9651994205913, (16, 18540): 1623.970678935285, (16, 18541): 1624.7517960069674, (16, 18542): 1625.2861931880511, (16, 18543): 1622.4665533604596, (16, 18546): 1623.119410099505, (16, 18555): 1626.156222432294, (16, 18556): 1626.432952242028, (16, 18565): 1628.47694561759, (16, 18567): 1628.5696476213197, (16, 18568): 1627.25326794473, (16, 18577): 1639.315789935601, (16, 18583): 1638.4057541102911, (16, 18605): 1642.2800998330424, (16, 18608): 1627.9796361070096, (16, 18616): 1653.4678708657202, (16, 18618): 1662.2838668297568, (16, 18625): 1661.9849770475607, (16, 18645): 1654.7501734003908, (16, 18646): 1655.9801594633211, (16, 18653): 1645.1682836367825, (16, 18654): 1652.73924826853, (16, 18655): 1647.1528325914578, (16, 18666): 1683.2089477084935, (16, 18837): 1691.8494581828243, (16, 18974): 1632.2487075312185, (16, 18999): 1645.3155080970118, (16, 19000): 1648.3299851298352, (16, 19174): 1535.457159597228, (16, 19342): 1604.8801561523742, (16, 19455): 1535.7450604623714, (16, 19555): 1407.8411403852856, (16, 19564): 1432.089433334395, (16, 19573): 1422.5160365827553, (16, 19586): 1417.2203679299535, (16, 19605): 1417.0377382615693, (16, 19611): 1422.9095578599238, (16, 19614): 1415.9713988999397, (16, 19641): 1495.1690401527142, (16, 19702): 1498.5656757019474, (16, 19713): 1491.778454013854, (16, 19731): 1360.8733683690953, (16, 19819): 1522.4737547847894, (16, 19893): 1144.3299483734436, (16, 19899): 1165.102315640242, (16, 19929): 1153.134360593128, (16, 19951): 1207.1809864029758, (16, 19962): 1150.9699995530907, (16, 19970): 1175.946868776849, (16, 19971): 1173.1314549983026, (16, 19972): 1166.373743923641, (16, 19975): 1166.3962403922537, (16, 19978): 1232.210211226249, (16, 19987): 1235.170852767243, (16, 19989): 1219.9596704232374, (16, 20039): 1238.9621757609295, (16, 20043): 1248.1460696292663, (16, 20047): 1245.715745587305, (16, 20052): 1226.6194874929586, (16, 20054): 1226.5997528160324, (16, 20085): 1322.6127944279033, (16, 20104): 1328.148821504763, (16, 20132): 1291.5875087045629, (16, 20203): 1113.2364278214504, (16, 20280): 1098.0315463996715, (16, 20285): 1092.7218954073087, (16, 20290): 1102.494959241911, (16, 20297): 1097.850765891308, (16, 20309): 1215.5679759705554, (16, 20453): 1319.221209718704, (16, 20485): 1068.285029106665, (16, 20520): 1057.453333501168, (16, 20526): 1042.7955822648235, (16, 20698): 1145.8709758518985, (16, 20868): 1169.617556942479, (16, 21042): 1070.938718586596, (16, 21057): 1112.6871553889246, (16, 21066): 1087.4879589928712, (16, 21075): 1086.456873947311, (16, 21093): 1067.4688521490552, (16, 21098): 1087.665969020962, (16, 21127): 1070.8425745853945, (16, 21130): 1075.4724922672772, (16, 21144): 1080.4971864178092, (16, 21146): 1068.1623023647328, (16, 21147): 1081.6718324206704, (16, 21148): 1086.676286164093, (16, 21153): 1094.2749064680386, (16, 21293): 1131.5238819666076, (16, 21426): 1180.56377391223, (16, 21442): 1234.9255880949945, (16, 21451): 1239.887958057748, (16, 21466): 1204.419637212319, (16, 21469): 1209.5420486866715, (16, 21471): 1201.957923021731, (16, 21473): 1205.4567624154965, (16, 21475): 1201.519023759635, (16, 21482): 1215.1956017842226, (16, 21484): 1212.8558998731764, (16, 21488): 1210.5079322045447, (16, 21494): 1198.1184872262058, (16, 21498): 1202.7979878334793, (16, 21500): 1192.7364213287192, (16, 21514): 1192.2503653222966, (16, 21537): 1184.0074658957133, (16, 21662): 1188.9557275920383, (16, 21691): 1165.582497495267, (16, 21757): 1150.1713254315591, (16, 21777): 970.8978879662981, (16, 21778): 965.0801215265857, (16, 21779): 965.0948473459986, (16, 21790): 980.9525196241744, (16, 21802): 974.3418347821832, (16, 21824): 977.2607946933314, (16, 21874): 962.6579497263588, (16, 21879): 953.3253242878922, (16, 21983): 1010.5119891238322, (16, 22002): 1052.8147214786513, (16, 22132): 1087.3194743148474, (16, 22261): 229.46620681066474, (16, 22298): 216.17316314735973, (16, 22339): 186.64419171580337, (16, 22508): 273.62039825928963, (16, 22841): 1932.361070476656, (16, 22842): 1930.8476136133663, (16, 22874): 1911.0278674058684, (16, 22941): 1917.7777954237197, (16, 22956): 1925.3131973686548, (16, 22960): 1931.6340420234048, (16, 22968): 1919.3048756481671, (16, 22970): 1924.7815389491395, (16, 22974): 1915.911656319494, (16, 22980): 1926.4721684728145, (16, 23025): 1906.3655982645028, (16, 23028): 1900.0673411519113, (16, 23081): 1894.4213507272834, (16, 23104): 1842.9427494056947, (16, 23147): 1803.8178652799447, (16, 23298): 1280.2508166085404, (16, 23376): 1261.55491660672, (16, 23381): 1237.0155833641643, (16, 23529): 1281.4077218745222, (16, 23556): 1272.234843261027, (16, 23718): 1279.9300245063862, (16, 24001): 1394.089937851535, (16, 24094): 1407.9264378231242, (16, 24129): 1426.7383236212656, (16, 24174): 1379.4712571622933, (16, 24235): 1415.9504036565663, (16, 24259): 1439.2314180363187, (16, 24260): 1437.0782272100657, (16, 24261): 1433.7989238951036, (16, 24305): 1462.9202779051316, (16, 24306): 1465.4966435337983, (16, 24307): 1460.6288203060033, (16, 24308): 1454.5802518856233, (16, 24498): 1526.1025447477825, (16, 24499): 1526.138386330592, (16, 24500): 1523.0741325481233, (16, 24668): 1519.7971545773994, (16, 24711): 1541.1019623222735, (16, 24756): 1547.0833547091054, (16, 24788): 1555.1904013319543, (16, 24809): 1527.8688697001098, (16, 24813): 1536.9336034025239, (16, 24821): 1534.1991057923021, (16, 24825): 1535.1749056572717, (16, 24832): 1526.8565145095772, (16, 24833): 1530.4209525109563, (16, 24835): 1533.6539772137787, (16, 24837): 1540.0682736631857, (16, 24840): 1525.9223440203202, (16, 24841): 1532.2212055435675, (16, 24844): 1525.5673563155392, (16, 24845): 1530.8353532415438, (16, 24846): 1527.6838152241555, (16, 24849): 1529.3792897629776, (16, 24850): 1537.3910150764832, (16, 24863): 1491.5824930722733, (16, 24866): 1498.144083042212, (16, 24885): 1503.9595481201022, (16, 24886): 1503.3852776098647, (16, 24889): 1521.399962975783, (16, 24903): 1528.5766130979946, (16, 24909): 1508.0531901635575, (16, 24999): 1795.8132250080362, (16, 25019): 1792.4076985134402, (16, 25028): 1791.1761320683677, (16, 25137): 1075.8849881592234, (16, 25145): 1083.5112034745282, (16, 25208): 1144.8146950491243, (16, 25233): 1133.6839794706493, (16, 25371): 1095.5820237056532, (16, 25377): 1080.3763163810474, (16, 25828): 732.0199489172267, (16, 25851): 700.0679636403308, (16, 25874): 741.3508425927945, (16, 25898): 746.6309450844717, (16, 25946): 727.8647165365168, (16, 26047): 808.366600418678, (16, 26066): 1001.8779507272924, (16, 26197): 887.7470002777037, (16, 26212): 512.7429127508697, (16, 26253): 490.77936124716814, (16, 26254): 500.2244674562736, (16, 26257): 504.5007272389938, (16, 26258): 494.2035666320243, (16, 26260): 499.7483845529693, (16, 26266): 499.344914407424, (16, 26267): 504.6069553254706, (16, 26271): 503.8360015507794, (16, 26304): 584.5857677382841, (16, 26305): 586.5362372445991, (16, 26363): 695.739571982812, (16, 26441): 15.483535882011326, (16, 26442): 18.780581585421018, (16, 26450): 22.40451400822774, (16, 26459): 16.504352870181975, (16, 26462): 14.98284034506468, (16, 26467): 17.116177536334764, (16, 26471): 10.356595145681828, (16, 26472): 10.945982636176845, (16, 26473): 12.19112639220851, (16, 26476): 29.14654315663022, (16, 26485): 14.785931715892074, (16, 26493): 19.915803082658794, (16, 26524): 12.854472483415734, (16, 26525): 12.128705744497243, (16, 26556): 6.533152577643613, (16, 26560): 6.5463262117808725, (16, 26561): 10.040033474024678, (16, 26564): 8.027526132321034, (16, 26569): 8.094261796694093, (16, 26570): 8.658034920978846, (16, 26573): 7.96827321177342, (16, 26581): 11.779486324602143, (16, 26583): 11.09931818644815, (16, 26593): 17.557289280654537, (16, 26837): 20.240853219161533, (16, 26844): 26.91788314454376, (16, 26863): 23.608064736825884, (16, 26893): 38.2669125854293, (16, 26902): 45.95932587599321, (16, 26905): 33.07250153491951, (16, 26912): 41.09798003816357, (16, 26921): 29.14250040583069, (16, 26922): 42.43485643125925, (16, 27212): 263.23627324894153, (16, 27218): 270.6631558932851, (16, 27239): 266.4124766254121, (16, 27257): 259.90826008832937, (16, 27274): 265.55171544091354, (16, 27279): 260.93668354493246, (16, 27282): 257.8436653849082, (16, 27283): 266.7622037549628, (16, 27285): 264.6755509141129, (16, 27286): 254.80670094385695, (16, 27290): 254.7208587301603, (16, 27295): 259.07533428384056, (16, 27300): 267.66459365072086, (16, 27344): 241.61646265449636, (16, 27366): 241.02227335204353, (16, 27383): 256.75641221783394, (16, 27398): 270.53795124339035, (16, 27406): 269.9224803400717, (16, 27407): 274.05483300629027, (16, 27426): 296.67636873681954, (16, 27432): 277.5129073754076, (16, 27460): 292.80856541475316, (16, 27523): 181.1346665300346, (16, 27545): 333.5567218290165, (16, 27602): 469.60346003427884, (16, 27606): 475.03468778771395, (16, 27646): 265.40692571478985, (16, 27667): 296.21093495322725, (16, 27672): 299.4306542009366, (16, 27674): 293.0959025242237, (16, 27688): 303.93893748758654, (16, 27692): 303.14159094403317, (16, 27693): 298.0607872389233, (16, 27705): 296.078149930183, (16, 27712): 297.1583240621562, (16, 27786): 545.1833462007774, (16, 27790): 556.9491422207558, (16, 27791): 559.8538265055706, (16, 27795): 534.7561614884036, (16, 27801): 540.8492168039234, (16, 27813): 546.6917923568127, (16, 27816): 546.6105110413242, (16, 27823): 541.3692533723196, (16, 27830): 546.4710658672359, (16, 27884): 194.9621746881569, (16, 27885): 249.73907855413154, (16, 27896): 217.75766498054935, (16, 27919): 217.60836879481536, (16, 27922): 221.3657781291114, (16, 27930): 205.95670674293953, (16, 27934): 206.19578864204982, (16, 27935): 205.66022051274385, (16, 27948): 398.8754010851976, (16, 27951): 420.55439387155667, (16, 28061): 394.53818614197615, (16, 28290): 662.3853176375447, (16, 28292): 674.8597981040494, (16, 28293): 665.215473796457, (16, 28295): 665.5279075021293, (16, 28296): 663.7701171935344, (16, 28297): 656.1712989640922, (16, 28302): 656.5242996862947, (16, 28310): 1181.5101225449835, (16, 28313): 1198.800758472281, (16, 28372): 1175.829149230223, (16, 28398): 1178.1127030453072, (16, 28399): 1177.5864567140527, (16, 28400): 1181.548447871856, (16, 28401): 1168.156534969905, (16, 28445): 1202.9935561067784, (16, 28475): 1143.468943538849, (16, 28885): 1381.1403565387177, (16, 28886): 1376.1504070200288, (16, 28915): 1373.186790507485, (16, 28916): 1372.1374854392973, (16, 28917): 1368.9429723713172, (16, 28921): 1388.9565562874316, (16, 28931): 1386.4184311810784, (16, 28945): 1348.9295965826823, (16, 28982): 1359.8297958017954, (16, 29219): 1347.924464235221, (16, 29228): 1333.7953235168804, (16, 29246): 1411.1969895993395, (16, 29248): 1404.2888309095006, (16, 29282): 1386.7185429468605, (16, 29290): 1426.2355502290684, (16, 29291): 1420.9007594072175, (16, 29292): 1425.0906469454683, (16, 29293): 1417.9441904092855, (16, 29294): 1421.2483477312046, (16, 29298): 1416.9980602778874, (16, 29299): 1414.8780541138406, (16, 29304): 1411.5444878304559, (16, 29317): 1396.4678740551442, (16, 29323): 1395.4745558591985, (16, 29330): 1402.4558546046064, (16, 29331): 1407.2053046408932, (16, 29344): 1337.6765092408007, (16, 29445): 1149.892597676155, (16, 29724): 1967.7683618439203, (16, 29738): 1970.4318101911185, (16, 29745): 1964.9232960075815, (16, 29748): 1977.9233164531317, (16, 29750): 1987.1040761309023, (16, 29759): 1972.8683498932285, (16, 29772): 1982.8891621036669, (16, 29781): 1981.0296502427282, (16, 29784): 1974.3948872148856, (16, 29790): 1985.2311658163226, (16, 29811): 1984.6178535954418, (16, 29817): 2033.066152113914, (16, 29818): 2031.4562328649379, (16, 29929): 1956.8509957965264, (16, 30039): 1960.124900184647, (16, 30066): 1919.3112259894085, (16, 30116): 1853.1589374378993, (16, 30238): 1756.8348975606798, (16, 30248): 1770.2848330186023, (16, 30260): 1768.4518397021204, (16, 30545): 1350.0305293525394, (16, 30733): 1208.6837070135978, (16, 30756): 1133.568855389395, (16, 30921): 1220.8511361849519, (16, 31079): 1063.021638035408, (16, 31149): 1008.6886812833735, (16, 31154): 1014.9629523217196, (16, 31160): 1006.7699925395299, (16, 31163): 1012.5854466526416, (16, 31189): 937.7090860396803, (16, 31215): 947.7594615938714, (16, 31259): 967.6466333418891, (16, 31262): 958.2239264488445, (16, 31430): 1087.073582057687, (16, 31568): 964.6068245752765, (16, 31751): 1041.664868806055, (17, 109): 1292.2262324327103, (17, 872): 686.2555533492671, (17, 873): 692.5070541771868, (17, 877): 688.3506396481322, (17, 879): 689.1079452138831, (17, 884): 678.778623885444, (17, 889): 683.5781289455189, (17, 891): 677.1783239949456, (17, 892): 694.3630751903493, (17, 894): 694.2971692400047, (17, 896): 691.2711218845986, (17, 903): 686.5416376899643, (17, 909): 681.9130931787071, (17, 910): 686.1157699214505, (17, 912): 681.638436458539, (17, 913): 676.0729231174645, (17, 916): 676.3059736666933, (17, 926): 690.4233748498972, (17, 927): 688.7527257240445, (17, 948): 675.196177431493, (17, 961): 686.1501751308687, (17, 962): 688.0541315283866, (17, 963): 689.8084380314277, (17, 967): 689.9336568054553, (17, 974): 682.4082934867895, (17, 998): 690.985813589765, (17, 1014): 854.7144292614422, (17, 1086): 726.459219445387, (17, 1087): 733.1422829186951, (17, 1089): 724.0998033542542, (17, 1090): 725.8426368229548, (17, 1092): 733.9363753201749, (17, 1097): 726.2981287746792, (17, 1107): 742.6206275443827, (17, 1387): 900.065060900419, (17, 1554): 973.3274198149891, (17, 1827): 982.018257932185, (17, 1828): 983.1980010053251, (17, 1829): 984.1175059574892, (17, 1830): 981.2058544010056, (17, 1831): 982.1912105048407, (17, 1832): 981.5304890116663, (17, 1833): 981.9136755958039, (17, 1836): 981.3623251278193, (17, 1841): 985.8331010788705, (17, 1843): 983.7791742576038, (17, 1844): 984.4072979833927, (17, 1845): 981.7097455703728, (17, 1847): 974.6586324543828, (17, 1848): 977.2717719510434, (17, 1849): 989.2744578772946, (17, 1850): 990.8263903574655, (17, 1851): 978.5004477966811, (17, 1852): 978.0351163779022, (17, 1854): 979.812881881731, (17, 1856): 973.3880241862526, (17, 1857): 976.7231928269714, (17, 1858): 988.5325409043837, (17, 1861): 983.3658199020038, (17, 1866): 972.6419621602353, (17, 1867): 986.5397773854525, (17, 1868): 985.4482205475063, (17, 1870): 983.3340432894613, (17, 1871): 986.7383606951186, (17, 1875): 980.1269666137463, (17, 1880): 975.642796408938, (17, 1882): 975.466136473334, (17, 1883): 991.679397219466, (17, 1889): 978.1720956591045, (17, 1893): 985.3931043201856, (17, 1894): 983.693084780334, (17, 1899): 976.9724022008464, (17, 1900): 978.6116410186753, (17, 1902): 988.6922725987887, (17, 1905): 990.6968125844888, (17, 1907): 979.7890478997114, (17, 1910): 981.5482157159571, (17, 1917): 998.1317314078872, (17, 1920): 980.5813271810613, (17, 1935): 992.3645212708892, (17, 1937): 994.2252400315587, (17, 1946): 974.3698880416587, (17, 1949): 977.092207405402, (17, 1950): 967.0050509240003, (17, 1951): 971.474728907637, (17, 1952): 972.6630045322163, (17, 1953): 975.6307105771001, (17, 1954): 972.5185035505787, (17, 1958): 975.6430525645015, (17, 1960): 979.1980140248157, (17, 1968): 980.6088696355795, (17, 1969): 994.2199815388063, (17, 1974): 990.5341204620121, (17, 1975): 990.0433332633033, (17, 1979): 985.191054609148, (17, 1980): 983.3581994047831, (17, 1981): 985.9070653432599, (17, 1985): 987.6798816882707, (17, 1994): 960.6677721897715, (17, 2011): 974.9309123223446, (17, 2019): 993.4697700139676, (17, 2020): 990.994690243259, (17, 2029): 980.4610249334414, (17, 2030): 989.300215747546, (17, 2032): 978.1446723823856, (17, 2033): 984.320438471524, (17, 2034): 983.6462521315489, (17, 2036): 970.96919508675, (17, 2037): 974.2936726395358, (17, 2038): 977.8802043225439, (17, 2042): 1008.2707200337304, (17, 2050): 983.8135425875793, (17, 2051): 982.7366511078661, (17, 2053): 983.8209199100127, (17, 2054): 986.4820348055393, (17, 2066): 980.9556835420591, (17, 2067): 981.3024563047164, (17, 2071): 955.9896662831562, (17, 2072): 961.5274010069184, (17, 2073): 949.6330732565353, (17, 2074): 948.4859313126196, (17, 2080): 938.8585669613556, (17, 2082): 964.3575527172484, (17, 2083): 967.2633730632091, (17, 2089): 962.2168042258006, (17, 2090): 965.0490585166174, (17, 2092): 962.1225096573162, (17, 2098): 943.0397597497235, (17, 2099): 945.5397365082871, (17, 2101): 941.871421156248, (17, 2102): 956.4644646331446, (17, 2103): 951.6188700776304, (17, 2104): 948.6730177460678, (17, 2106): 968.7672362098317, (17, 2112): 943.2227540973139, (17, 2113): 958.1558300355995, (17, 2114): 960.60660571157, (17, 2117): 970.4314630452678, (17, 2123): 979.0751938163647, (17, 2124): 982.0417904244049, (17, 2134): 971.2483068831124, (17, 2138): 980.9128837880179, (17, 2141): 972.9918933272686, (17, 2148): 968.7082041726159, (17, 2150): 965.3370447387541, (17, 2151): 967.8004025518013, (17, 2152): 963.0823021076603, (17, 2153): 970.5033097972455, (17, 2154): 958.6838228284666, (17, 2155): 955.8505215899378, (17, 2156): 954.5639775726893, (17, 2157): 952.6735957060953, (17, 2160): 980.8235275486512, (17, 2161): 961.6815976572362, (17, 2162): 967.9298923861083, (17, 2163): 964.0069467125799, (17, 2164): 963.2381768647998, (17, 2168): 962.0069646291089, (17, 2172): 960.9161178094465, (17, 2174): 966.3198405388354, (17, 2178): 962.2597344614205, (17, 2179): 960.0228554535398, (17, 2183): 979.6729781124261, (17, 2185): 979.3104548018913, (17, 2186): 977.2306655569533, (17, 2190): 982.352499305929, (17, 2192): 978.4064526748543, (17, 2193): 980.8141331017239, (17, 2194): 976.7964630083255, (17, 2195): 975.0297300171853, (17, 2197): 978.7061209273975, (17, 2205): 971.4359123748989, (17, 2207): 962.3418980680998, (17, 2208): 967.2011937921696, (17, 2212): 984.6132406343596, (17, 2214): 882.4470206829608, (17, 2225): 889.414054574422, (17, 2231): 895.889427992628, (17, 2278): 925.0047181443322, (17, 2284): 932.2737898418067, (17, 2285): 930.4781020493361, (17, 2291): 909.3872127267014, (17, 2292): 915.8454632839715, (17, 2307): 926.4866667967763, (17, 2313): 905.982150376659, (17, 2317): 911.397911889093, (17, 2319): 918.3740890881784, (17, 2321): 921.6053601514438, (17, 2323): 922.3952267488663, (17, 2326): 940.1093359911936, (17, 2327): 936.3558371711662, (17, 2329): 933.6528714293022, (17, 2330): 930.2498641681719, (17, 2332): 935.801888728147, (17, 2344): 928.2123974516994, (17, 2346): 927.0619337511628, (17, 2361): 934.2551701976317, (17, 2368): 972.7846295855213, (17, 2374): 976.1759532224359, (17, 2375): 978.0325260764632, (17, 2377): 964.3695968927495, (17, 2378): 980.2245982363884, (17, 2379): 979.6453553624466, (17, 2380): 981.7330637787973, (17, 2383): 968.7962597513304, (17, 2385): 971.3548560661034, (17, 2395): 972.4907570885297, (17, 2397): 977.512764593469, (17, 2398): 959.9204922848373, (17, 2399): 965.5158799719874, (17, 2400): 964.3856689624664, (17, 2402): 969.8323586326566, (17, 2403): 972.9694780243696, (17, 2404): 974.1644120591355, (17, 2405): 966.2595021334064, (17, 2407): 973.2643484050265, (17, 2408): 976.5402949939881, (17, 2409): 968.8057530585631, (17, 2411): 971.4009569405539, (17, 2412): 971.1505562322418, (17, 2413): 973.5204673226552, (17, 2414): 969.1149431777858, (17, 2422): 969.9115933825312, (17, 2424): 972.377394353376, (17, 2426): 973.3745532093582, (17, 2433): 966.8959648391287, (17, 2436): 964.3192549651526, (17, 2437): 946.2186374738412, (17, 2440): 950.4830750524271, (17, 2445): 1025.652588583807, (17, 2447): 1016.0363935335533, (17, 2454): 1025.7327649719527, (17, 2455): 1026.8436776326494, (17, 2460): 996.0043415104952, (17, 2461): 999.6775666029496, (17, 2471): 1057.1235767643077, (17, 2492): 978.8882353312548, (17, 2511): 948.8945510887557, (17, 2523): 964.1051650865934, (17, 2525): 958.9453637892422, (17, 2535): 973.1505121577347, (17, 2537): 966.0629066274464, (17, 2538): 971.3604263401287, (17, 2539): 967.4406401089997, (17, 2540): 976.3153809107755, (17, 2542): 980.7686243234432, (17, 2559): 1082.8222238272565, (17, 2575): 1071.614204882926, (17, 2599): 931.0643921338816, (17, 2600): 961.8707779820214, (17, 2607): 946.341014536517, (17, 2627): 965.2996706491767, (17, 2647): 983.6659981427341, (17, 2674): 974.4790317647407, (17, 2681): 971.6916139558687, (17, 2683): 980.8251468475543, (17, 2686): 970.5491732829906, (17, 2689): 1091.2771084598446, (17, 2690): 1091.8615087587714, (17, 2713): 1117.0584512675719, (17, 2714): 1119.6044907970124, (17, 2715): 1122.5839183866121, (17, 2739): 1119.7898163739512, (17, 2740): 1099.7990610727566, (17, 2741): 1101.2150234025414, (17, 2749): 1116.2392032905284, (17, 2750): 1116.9734838272611, (17, 2752): 1119.0113965116357, (17, 2755): 1121.4905176020357, (17, 2758): 1120.9692185337458, (17, 2759): 1120.8897131524618, (17, 2769): 1117.205087375904, (17, 2771): 1104.8810332071687, (17, 2779): 1107.0165645672205, (17, 2784): 1074.048342691919, (17, 2800): 1081.8086457544832, (17, 2802): 1094.5582884183093, (17, 2803): 1093.2849788539013, (17, 2804): 1091.2365092572861, (17, 2805): 1097.5263111072466, (17, 2807): 1097.1818780605097, (17, 2809): 1096.43107809651, (17, 2812): 1076.8484718831498, (17, 2814): 1096.6760711632899, (17, 2817): 1099.4591097339096, (17, 2819): 1097.2114637439877, (17, 2823): 1080.2678579063158, (17, 2832): 1101.4733976060218, (17, 2836): 1087.9899359655776, (17, 2839): 1096.9850273675515, (17, 2841): 1098.986185835611, (17, 2843): 1097.6131656189564, (17, 2846): 1091.3836516002818, (17, 2849): 1103.8724483345632, (17, 2852): 1100.696233277708, (17, 2853): 1105.3465748913995, (17, 2876): 1107.6273283480068, (17, 2877): 1118.5940693039092, (17, 2885): 1124.1836244090387, (17, 2918): 1097.970489428133, (17, 2921): 1102.7466334317025, (17, 2925): 1080.2167840243176, (17, 2926): 1072.7646501053318, (17, 2930): 1090.3521364416904, (17, 2931): 1082.3935648507572, (17, 2938): 1098.2158357567796, (17, 2940): 1110.998633465146, (17, 2947): 1095.0052483432555, (17, 2949): 1089.7778836439422, (17, 2950): 1092.0481611205194, (17, 2952): 1089.7563764635277, (17, 2958): 1089.2326241859912, (17, 2959): 1091.249469818122, (17, 2960): 1096.4286371945286, (17, 2961): 1094.051239085352, (17, 2963): 1087.3941149604038, (17, 2968): 1088.9732046230495, (17, 2976): 1086.6704383435965, (17, 2981): 1044.7259508455463, (17, 2982): 1043.8500169719323, (17, 2984): 1041.6711378472978, (17, 3003): 1038.144110532251, (17, 3046): 1005.263020645467, (17, 3050): 1029.6632535873437, (17, 3051): 1031.3572487144936, (17, 3053): 1026.46030285525, (17, 3069): 1054.9494416510142, (17, 3071): 1024.7000573603384, (17, 3080): 1125.2240196445052, (17, 3199): 1033.8926888969431, (17, 3200): 1029.0362168038175, (17, 3205): 1061.1621145044794, (17, 3209): 1031.859070483976, (17, 3215): 1029.0214287724036, (17, 3217): 1022.6289002944499, (17, 3249): 1029.2535999132404, (17, 3263): 1077.4527751162755, (17, 3289): 1043.6376844179058, (17, 3301): 1045.9791630463287, (17, 3302): 1043.3698985803148, (17, 3307): 1040.4087893848475, (17, 3310): 1048.7354330129556, (17, 3391): 1079.7944203579193, (17, 3509): 8.297909524473125, (17, 3510): 12.850875041025171, (17, 3511): 11.235098873997629, (17, 3512): 15.437359756640019, (17, 3514): 16.569045185608296, (17, 3519): 15.809878909751262, (17, 3536): 8.345680219179034, (17, 3545): 13.905046274442519, (17, 3548): 16.637067615494843, (17, 3572): 4.841753804366486, (17, 3581): 8.271825694006322, (17, 3583): 9.180860925859607, (17, 3601): 24.382658662939196, (17, 3656): 34.99226436833753, (17, 3669): 63.897654366998836, (17, 3670): 65.16501392687455, (17, 3695): 57.25679747075451, (17, 3696): 55.598306994287036, (17, 3782): 78.87576622853341, (17, 3792): 69.5181541530465, (17, 3989): 1974.904957093258, (17, 4008): 1998.6123750118857, (17, 4031): 1994.4146685489734, (17, 4045): 1988.5319638197939, (17, 4144): 1992.307786602367, (17, 4145): 1971.2114316645207, (17, 4164): 1983.7877330993983, (17, 4168): 1977.6549620852404, (17, 4173): 1976.773238738835, (17, 4181): 1962.3195425732033, (17, 4228): 1945.8041405222277, (17, 4248): 1943.7402199325022, (17, 4254): 1825.9461004243135, (17, 4260): 1825.227757941811, (17, 4262): 1834.3245903720544, (17, 4273): 1831.74780126153, (17, 4319): 1758.992344084427, (17, 4326): 1756.1437043107453, (17, 4328): 1756.869128549843, (17, 4334): 1762.6191057773508, (17, 4335): 1760.9330013501733, (17, 4372): 1729.5356836250653, (17, 4413): 1806.9374364691482, (17, 4434): 1726.4081849820107, (17, 4447): 1737.0597202758647, (17, 4452): 1727.4313217025665, (17, 4463): 1565.5264244678388, (17, 4465): 1571.0636573463073, (17, 4619): 1814.4906024627135, (17, 4645): 1832.0248926159124, (17, 4657): 1829.0757415337073, (17, 4666): 1822.1602973774068, (17, 4676): 1834.2404110250084, (17, 4678): 1837.0438085597232, (17, 4689): 1828.5399333925689, (17, 4704): 1888.4598883281453, (17, 4726): 2026.3227282744233, (17, 4727): 2023.7430222918447, (17, 4730): 2018.7734323568538, (17, 4731): 2019.9817165025656, (17, 4734): 2024.051593055541, (17, 4735): 2021.419911685756, (17, 4736): 2022.487810451665, (17, 4737): 2017.9296275312233, (17, 4738): 2018.3758224603027, (17, 4756): 2020.8541095273636, (17, 4760): 2008.8574766778409, (17, 4761): 2010.6991160396772, (17, 4762): 2005.1019087097868, (17, 4765): 2010.0117634906649, (17, 4773): 2031.585654643668, (17, 4774): 2028.9127810116595, (17, 4790): 2029.9270148391397, (17, 4795): 2027.766990212913, (17, 4799): 2029.8325188635563, (17, 4801): 2034.7350313227057, (17, 4804): 2029.110464946418, (17, 4805): 2027.3312415211753, (17, 4806): 2027.3875946968524, (17, 4815): 2024.5891983695656, (17, 4816): 2031.2243556558578, (17, 4817): 2032.080859915602, (17, 4826): 2028.3582120778615, (17, 4830): 2024.5089627536197, (17, 4839): 2016.3407864041244, (17, 4840): 2018.45701431338, (17, 4841): 2012.878574948472, (17, 4846): 2011.1649024798226, (17, 4848): 2010.210897537477, (17, 4850): 2012.4900212960379, (17, 4871): 1984.3312837246563, (17, 4883): 2006.4972254694108, (17, 4900): 1995.621206983168, (17, 4901): 1992.12159776578, (17, 4917): 1805.8132813631294, (17, 4931): 1786.5421925149742, (17, 4944): 1808.2965851858057, (17, 4956): 1789.7764120960273, (17, 4958): 1788.6290204427999, (17, 4959): 1784.5670590288541, (17, 4961): 1793.9206168971702, (17, 4966): 1784.7235792124425, (17, 5207): 1763.3081049067175, (17, 5272): 1419.9217825071798, (17, 5283): 1426.5592871120234, (17, 5287): 1435.2771283774673, (17, 5289): 1438.130104440035, (17, 5293): 1423.0523494714187, (17, 5295): 1441.8818928621656, (17, 5296): 1440.5702854919195, (17, 5298): 1439.6958458968456, (17, 5303): 1444.2860912223448, (17, 5305): 1413.7532569119196, (17, 5306): 1406.8806923766963, (17, 5307): 1410.1613176202882, (17, 5308): 1416.473705758086, (17, 5313): 1417.6519710356138, (17, 5314): 1422.3372878383311, (17, 5317): 1415.7677175812798, (17, 5319): 1437.5033415340527, (17, 5324): 1434.5782419162717, (17, 5326): 1432.7735622531366, (17, 5348): 1404.3348659099788, (17, 5351): 1407.7611290245754, (17, 5399): 1440.3142023909654, (17, 5413): 1413.990753207639, (17, 5422): 1445.079921622736, (17, 5445): 1429.1154199352245, (17, 5448): 1422.6575392756715, (17, 5456): 1419.943831923979, (17, 5467): 1425.6377327977914, (17, 5624): 1358.9164392357904, (17, 5671): 1583.8008837890504, (17, 5672): 1575.1303680450917, (17, 5797): 1688.5768860376663, (17, 5871): 1522.7216996558552, (17, 5976): 1444.8765421646194, (17, 6118): 625.2434506837067, (17, 6248): 760.8345618663793, (17, 6345): 1063.3421070993993, (17, 6352): 1043.0519527369113, (17, 6354): 1067.9511705715593, (17, 6359): 1072.627013296252, (17, 6376): 1048.0406042410946, (17, 6378): 1065.6096082546424, (17, 6381): 1071.4255525594424, (17, 6383): 1058.7601687451477, (17, 6396): 1071.9537665867995, (17, 6399): 1064.418006158812, (17, 6408): 1043.0804932701144, (17, 6409): 1050.9296758295131, (17, 6419): 1015.332670140212, (17, 6422): 1044.3570326966508, (17, 6423): 1042.6156587356807, (17, 6424): 1064.1107207100356, (17, 6439): 1059.676246820819, (17, 6464): 1053.511720258082, (17, 6465): 1051.9938208899807, (17, 6469): 1055.7230369806473, (17, 6470): 1054.7536517224248, (17, 6472): 1079.7860231492587, (17, 6480): 1072.8872107786049, (17, 6486): 1082.887538710004, (17, 6497): 1079.3494644412701, (17, 6503): 1052.221853829414, (17, 6508): 1055.0296435415464, (17, 6509): 1058.414357698051, (17, 6521): 1074.417339833426, (17, 6544): 1071.701603860871, (17, 6552): 1045.166153941127, (17, 6553): 1041.8089906714504, (17, 6554): 1038.4122098742341, (17, 6578): 1050.9829253879734, (17, 6582): 1047.1200539846027, (17, 6601): 1052.2066754828472, (17, 6609): 1080.4306038110462, (17, 6610): 1081.056596142758, (17, 6611): 1082.5434339514647, (17, 6614): 1081.3400517644163, (17, 6615): 1081.645209250303, (17, 6616): 1084.0147623961252, (17, 6617): 1082.8712312029481, (17, 6618): 1086.7179497240425, (17, 6619): 1078.7607297116194, (17, 6620): 1083.5973480224889, (17, 6621): 1080.6770885752321, (17, 6622): 1081.6731334363008, (17, 6623): 1080.4503103175707, (17, 6624): 1077.3952482644402, (17, 6625): 1077.1454219135326, (17, 6626): 1078.843101586943, (17, 6627): 1081.1339278690211, (17, 6628): 1082.5319460681212, (17, 6629): 1077.562563790052, (17, 6630): 1075.585760726148, (17, 6632): 1077.5487129653213, (17, 6634): 1072.1924936030928, (17, 6635): 1079.9240925362058, (17, 6636): 1084.0021161598484, (17, 6637): 1073.6323699096874, (17, 6638): 1075.4115332625106, (17, 6639): 1081.0987522889059, (17, 6640): 1076.158642965459, (17, 6641): 1080.2351875327136, (17, 6642): 1075.1239785428893, (17, 6643): 1078.9221897592013, (17, 6645): 1078.9091876961322, (17, 6646): 1086.0786375273535, (17, 6647): 1076.1683251249233, (17, 6653): 1081.6842449110657, (17, 6655): 1081.311673204751, (17, 6658): 1071.7718626604155, (17, 6662): 1074.5908968793376, (17, 6819): 906.7451218178559, (17, 6996): 959.1974057061639, (17, 7059): 997.745957374366, (17, 7187): 942.3426682328881, (17, 7304): 851.1128655893676, (17, 7528): 957.8478042553554, (17, 7720): 1185.0232511682782, (17, 7793): 1181.2430727640883, (17, 7807): 1184.032484255017, (17, 7808): 1180.3865440900256, (17, 7831): 1098.072279740023, (17, 7850): 1136.2960898922208, (17, 7852): 1128.596955043786, (17, 8012): 1173.6356790048749, (17, 8125): 1216.578926021631, (17, 8208): 1255.9623325062216, (17, 8392): 1122.8814196504713, (17, 8651): 722.9763949945407, (17, 9088): 905.6315560344497, (17, 9443): 641.7833952432966, (17, 9444): 647.9219918641335, (17, 9828): 508.6128383131846, (17, 9868): 471.2227044818669, (17, 10180): 1221.5949865699245, (17, 10256): 1321.8383766725738, (17, 10276): 1273.4512497714798, (17, 10378): 1280.38834193605, (17, 10676): 1202.3404148523161, (17, 10714): 1142.2232340558592, (17, 10730): 1141.880674109137, (17, 10862): 1265.0511528813806, (17, 10881): 1280.3907352181031, (17, 10883): 1279.0496776891812, (17, 10885): 1261.6612837590185, (17, 10891): 1277.007154502004, (17, 10909): 1274.7986554736176, (17, 10911): 1276.0775188761395, (17, 10913): 1272.8164087679015, (17, 10915): 1272.2086365575892, (17, 10919): 1273.971340172092, (17, 11037): 1183.4680486669672, (17, 11039): 1139.7390938866538, (17, 11516): 2202.798207741602, (17, 11856): 1765.006587541624, (17, 11857): 1762.1357251450793, (17, 11861): 1763.7204290972709, (17, 11881): 1758.6239622663513, (17, 11902): 1741.6404812815788, (17, 11911): 1737.8578468810374, (17, 11914): 1740.5250394024206, (17, 11922): 1753.3916199550004, (17, 11924): 1757.2126960041944, (17, 11926): 1752.2787408658278, (17, 11950): 1761.1585045875206, (17, 11963): 1777.251304663436, (17, 11983): 1765.0334107983658, (17, 11985): 1785.391610088446, (17, 12009): 1781.0876298197672, (17, 12010): 1769.9650124852367, (17, 12018): 1771.6868976601704, (17, 12020): 1774.9523236475777, (17, 12021): 1776.7129156880117, (17, 12024): 1787.613668949575, (17, 12025): 1784.1680462457139, (17, 12027): 1781.5276998935572, (17, 12031): 1768.0639156181073, (17, 12032): 1772.0421548202994, (17, 12035): 1780.0915649103981, (17, 12041): 1787.4552145109183, (17, 12045): 1634.755248690901, (17, 12145): 1703.3498662815828, (17, 12275): 1980.2487766262504, (17, 12294): 1949.9271832765187, (17, 12358): 2039.079913760674, (17, 12463): 2072.9947328278063, (17, 12465): 2071.8969607217323, (17, 12482): 2088.053979008646, (17, 12503): 2085.7122782232304, (17, 12506): 2089.9033098495265, (17, 12549): 2081.8149095668177, (17, 12559): 2078.4177679580052, (17, 12569): 2081.503884532485, (17, 12572): 2084.6758349038437, (17, 12574): 2078.1553426826604, (17, 12576): 2085.5803655834916, (17, 12591): 2085.408492644422, (17, 12608): 2111.33813901648, (17, 12696): 2070.8795328483043, (17, 12710): 2095.5809309157253, (17, 12728): 2083.061520603622, (17, 12766): 1398.0504468133006, (17, 12771): 1368.2085645132559, (17, 12790): 1364.0018231399658, (17, 12795): 1354.1782381657235, (17, 12797): 1315.1473186476799, (17, 12798): 1320.6752614043555, (17, 12811): 1352.3586745817213, (17, 12830): 1341.4516881326088, (17, 12848): 1347.5777381299888, (17, 12850): 1350.6412399428489, (17, 12852): 1340.1155804727368, (17, 12854): 1335.2478268847308, (17, 12859): 1352.5867459712574, (17, 12861): 1326.2002210225598, (17, 12865): 1358.083967315184, (17, 12866): 1355.7439717266584, (17, 12867): 1365.3478693394893, (17, 12874): 1360.6653805451858, (17, 12875): 1364.4193156332285, (17, 12881): 1349.1267361322646, (17, 12883): 1355.16712593551, (17, 12885): 1367.5789851886423, (17, 12888): 1352.482604529413, (17, 12889): 1351.2314423454054, (17, 12892): 1361.6481271192317, (17, 12893): 1352.5930985070984, (17, 12896): 1355.6073385447448, (17, 12906): 1360.5393956852074, (17, 13018): 1315.8707726017903, (17, 13071): 1316.5781102990602, (17, 13131): 1277.4330125669162, (17, 13146): 1309.7607451733804, (17, 13159): 1265.6799588893716, (17, 13193): 1271.2562708475252, (17, 13198): 1215.4161872507614, (17, 13292): 1280.3533822011655, (17, 13296): 1299.8328935499126, (17, 13406): 1179.9240848300606, (17, 13407): 1178.1118845909614, (17, 13417): 1174.438483450517, (17, 13418): 1180.6607672772075, (17, 13438): 1204.7872583204908, (17, 13442): 1209.5450146005408, (17, 13443): 1204.8131022234768, (17, 13764): 828.0124329638539, (17, 13766): 833.6263595922965, (17, 13771): 831.2264412214911, (17, 13783): 818.362427234228, (17, 13784): 838.4805371969367, (17, 13792): 825.3717329329169, (17, 13824): 815.0695771501562, (17, 14017): 833.9878794553681, (17, 14870): 1248.7541531611969, (17, 14997): 915.7774871512077, (17, 15000): 917.8790483913907, (17, 15003): 923.5274988242154, (17, 15006): 926.2630433224614, (17, 15007): 930.5755247491468, (17, 15056): 934.378419668701, (17, 15063): 931.5502514403898, (17, 15069): 931.9181775592214, (17, 15076): 932.2322376225109, (17, 15086): 917.3533096908388, (17, 15087): 914.8197766511363, (17, 15111): 900.8951052871203, (17, 15116): 909.0312825306672, (17, 15722): 797.5454636093775, (17, 15998): 773.8941378826141, (17, 16073): 536.1379156889096, (17, 16939): 712.3991971804686, (17, 16940): 706.8334715765952, (17, 16951): 711.1892858342952, (17, 16963): 712.2030385058983, (17, 16965): 719.8788932230833, (17, 16969): 717.0178511480092, (17, 16970): 715.3623447606584, (17, 16971): 708.5160566226267, (17, 16973): 707.3610270648054, (17, 16974): 722.2969761603817, (17, 16976): 716.3470283473827, (17, 16978): 711.5966296211083, (17, 16980): 719.5028061612929, (17, 16982): 721.5373370329179, (17, 17045): 925.9674397533724, (17, 17048): 934.4449460904275, (17, 17304): 1912.5922670753569, (17, 17305): 1907.0540086429703, (17, 17330): 1911.4453633812986, (17, 17334): 1904.7172160320488, (17, 17343): 1917.2603636740037, (17, 17345): 1902.9799903176431, (17, 17347): 1909.948567995702, (17, 17351): 1893.6902190784165, (17, 17372): 1903.2664921364835, (17, 17373): 1917.0015206036478, (17, 17377): 1917.849006321538, (17, 17382): 1908.5999301466975, (17, 17383): 1910.8000805384631, (17, 17389): 1905.2252676206504, (17, 17400): 1914.8755862318192, (17, 17401): 1914.918869104114, (17, 17402): 1915.284317606776, (17, 17403): 1916.0903346214234, (17, 17440): 1901.991639607829, (17, 17455): 1914.6975940093726, (17, 17491): 1914.5266702162005, (17, 17507): 1902.5103827724333, (17, 17509): 1908.0810963850909, (17, 17590): 1888.5955327623706, (17, 17615): 1869.1663786531412, (17, 17642): 1873.6245827684613, (17, 17643): 1872.5935766087428, (17, 17668): 1869.3209139079543, (17, 17721): 1860.3701220539233, (17, 17754): 1910.4263266211883, (17, 17769): 1905.90832620517, (17, 17776): 1882.4785629231646, (17, 17804): 1914.6410742579453, (17, 17809): 1919.8824912963437, (17, 17824): 1917.4006013358373, (17, 17837): 1897.835156178284, (17, 17838): 1897.5752430515727, (17, 17862): 1893.280777244245, (17, 17866): 1904.8309054824556, (17, 17872): 1890.0214700966403, (17, 17873): 1881.0106008238674, (17, 17881): 1894.712655886397, (17, 17947): 398.94653610829835, (17, 17951): 387.7932109789067, (17, 17953): 388.7384262098386, (17, 17954): 391.51938610017675, (17, 17959): 391.4532213100837, (17, 17963): 382.26488360710283, (17, 18000): 335.92140620719306, (17, 18001): 342.2167329020959, (17, 18111): 616.7239518057548, (17, 18148): 450.04791986235847, (17, 18166): 518.8984482555182, (17, 18189): 561.6947443712796, (17, 18239): 1920.2097636237197, (17, 18240): 1919.9548129481504, (17, 18245): 1920.6005869742226, (17, 18247): 1919.2475775502255, (17, 18251): 1920.3465965537675, (17, 18256): 1921.3137582019629, (17, 18258): 1919.8860157354945, (17, 18259): 1920.0195220222863, (17, 18260): 1920.38577796579, (17, 18262): 1921.2239740353743, (17, 18263): 1921.5495527526234, (17, 18264): 1921.9261336663676, (17, 18266): 1921.4430438682834, (17, 18267): 1921.838902493735, (17, 18268): 1921.9617213336505, (17, 18269): 1922.7304513019615, (17, 18275): 1922.3668726419787, (17, 18285): 1921.8739739397272, (17, 18308): 1913.791646966828, (17, 18313): 1910.5099582188186, (17, 18314): 1911.4035747785692, (17, 18315): 1923.222945379593, (17, 18316): 1922.8950223932313, (17, 18317): 1923.238317114596, (17, 18320): 1923.9349057464397, (17, 18321): 1924.0072430093164, (17, 18322): 1924.6006983414493, (17, 18324): 1925.451902036509, (17, 18325): 1927.6557229416555, (17, 18326): 1926.8464871841443, (17, 18327): 1923.3373375381482, (17, 18329): 1928.9331799447045, (17, 18330): 1927.0305881330148, (17, 18331): 1925.6819477147135, (17, 18332): 1924.1600940070834, (17, 18333): 1927.029570855251, (17, 18336): 1926.1777396514956, (17, 18337): 1927.090823713611, (17, 18403): 1924.5286473026056, (17, 18432): 1887.0027166714594, (17, 18451): 1912.3955822822106, (17, 18466): 1937.81012580039, (17, 18481): 1924.4764405393714, (17, 18483): 1924.295550384, (17, 18484): 1923.2210997075624, (17, 18485): 1920.1686456394393, (17, 18486): 1924.0563517142455, (17, 18487): 1921.4530306496033, (17, 18489): 1923.1132108459083, (17, 18490): 1926.411387282414, (17, 18491): 1927.7391407645976, (17, 18492): 1918.467422940528, (17, 18493): 1923.7967107360319, (17, 18494): 1922.429170213492, (17, 18495): 1925.4487080154, (17, 18496): 1923.9109823916533, (17, 18497): 1921.0179621485815, (17, 18498): 1920.941661078816, (17, 18499): 1922.942622516505, (17, 18501): 1921.8084034969443, (17, 18502): 1920.5486399567424, (17, 18503): 1919.365762430596, (17, 18504): 1924.2411594416744, (17, 18506): 1922.5095333501026, (17, 18507): 1921.4090507969622, (17, 18508): 1922.8362193755052, (17, 18509): 1923.0301586648816, (17, 18510): 1919.6465169064497, (17, 18511): 1924.5445809664584, (17, 18512): 1922.6947478216675, (17, 18515): 1924.614671007599, (17, 18516): 1925.2979657069209, (17, 18517): 1923.9600040168182, (17, 18518): 1926.2011732182543, (17, 18519): 1924.4161140263823, (17, 18520): 1922.2452788199248, (17, 18522): 1929.532782814547, (17, 18523): 1930.0080828714945, (17, 18532): 1932.0842705350146, (17, 18535): 1927.9681350340693, (17, 18537): 1925.6763895852455, (17, 18539): 1926.2556414426147, (17, 18540): 1926.6281230624372, (17, 18541): 1927.843525490004, (17, 18542): 1928.5969674201226, (17, 18543): 1924.9322017078953, (17, 18546): 1926.9973808458665, (17, 18555): 1930.6074522726017, (17, 18556): 1931.393976342892, (17, 18565): 1932.0741364327243, (17, 18567): 1933.5014892245124, (17, 18568): 1931.37381762198, (17, 18577): 1945.4117904395455, (17, 18583): 1942.5364859431838, (17, 18605): 1944.8640584297948, (17, 18608): 1935.4662593239818, (17, 18616): 1958.0077655844661, (17, 18618): 1969.5189607943173, (17, 18625): 1964.3301998275413, (17, 18645): 1953.8913157003217, (17, 18646): 1956.917681617152, (17, 18653): 1948.8947566399033, (17, 18654): 1957.9454650691007, (17, 18655): 1952.2774861439102, (17, 18666): 1986.3121943789713, (17, 18837): 1927.0873417445714, (17, 18974): 1907.9249570308439, (17, 18999): 1915.088636509405, (17, 19000): 1918.419065887988, (17, 19174): 1750.1088584840475, (17, 19342): 1815.0839999968175, (17, 19455): 1781.8028893311732, (17, 19555): 1614.4117872870115, (17, 19564): 1622.4721364555414, (17, 19573): 1615.7290923132173, (17, 19586): 1612.8347306479743, (17, 19605): 1615.7696801999498, (17, 19611): 1620.3802062720613, (17, 19614): 1618.7683802314434, (17, 19641): 1697.9788661130249, (17, 19702): 1696.0718054173947, (17, 19713): 1690.3760444483873, (17, 19731): 1590.2588422181668, (17, 19819): 1755.1645541656799, (17, 19893): 1612.2607476332673, (17, 19899): 1650.4332799432764, (17, 19929): 1622.0211496156217, (17, 19951): 1697.0739204733384, (17, 19962): 1628.6359040790626, (17, 19970): 1644.1654645471726, (17, 19971): 1644.7201214521651, (17, 19972): 1638.5577567042944, (17, 19975): 1635.4338723043381, (17, 19978): 1712.1079163190875, (17, 19987): 1713.2958650573185, (17, 19989): 1692.6482957706244, (17, 20039): 1717.0472514427113, (17, 20043): 1725.5492547855185, (17, 20047): 1718.8394379521817, (17, 20052): 1696.1016171607453, (17, 20054): 1697.9558550003437, (17, 20085): 1800.8044777636833, (17, 20104): 1807.254449915488, (17, 20132): 1767.8504437200904, (17, 20203): 1610.2892628549305, (17, 20280): 1602.5233463752284, (17, 20285): 1600.6885465430212, (17, 20290): 1606.0097809366302, (17, 20297): 1598.9137106628796, (17, 20309): 1718.6320613741605, (17, 20453): 1825.1357063479807, (17, 20485): 1554.3884714813605, (17, 20520): 1536.420027511243, (17, 20526): 1530.4076917699463, (17, 20698): 754.1663751182896, (17, 20868): 627.5634775018212, (17, 21042): 1363.2737642910442, (17, 21057): 1406.0912820779834, (17, 21066): 1385.7327093782246, (17, 21075): 1376.7703610735623, (17, 21093): 1367.4130851075395, (17, 21098): 1399.1645636827661, (17, 21127): 1367.2779467884243, (17, 21130): 1375.8043189736484, (17, 21144): 1373.7314106146864, (17, 21146): 1364.4768665130355, (17, 21147): 1372.7670578569107, (17, 21148): 1380.494427862896, (17, 21153): 1359.8101428894408, (17, 21293): 1435.3687900855155, (17, 21426): 1418.3186856409811, (17, 21442): 1463.5317224536238, (17, 21451): 1467.9186964689861, (17, 21466): 1440.9883104764779, (17, 21469): 1447.883489965649, (17, 21471): 1437.4825696103046, (17, 21473): 1443.2334205062725, (17, 21475): 1438.145350814056, (17, 21482): 1452.0681586213639, (17, 21484): 1450.7220907810065, (17, 21488): 1446.6336066925921, (17, 21494): 1438.3475615488073, (17, 21498): 1443.4243333912625, (17, 21500): 1435.5914189517532, (17, 21514): 1450.3967793251436, (17, 21537): 1434.7383305541089, (17, 21662): 1457.3491915089153, (17, 21691): 1430.5108110789217, (17, 21757): 1380.510104034854, (17, 21777): 1283.947877599746, (17, 21778): 1277.216084402537, (17, 21779): 1281.495097181016, (17, 21790): 1290.9841332116803, (17, 21802): 1291.6214599557989, (17, 21824): 1299.1351513871564, (17, 21874): 1283.893574370372, (17, 21879): 1280.9417181151096, (17, 21983): 1304.3288807916515, (17, 22002): 1380.0869535279442, (17, 22132): 1325.777088180474, (17, 22261): 582.6422131512104, (17, 22298): 601.8004678129198, (17, 22339): 595.5618465597904, (17, 22508): 662.918475735357, (17, 22841): 1165.9079967263754, (17, 22842): 1164.7387988580174, (17, 22874): 1145.3690052150816, (17, 22941): 1151.0179811944267, (17, 22956): 1159.2991539865875, (17, 22960): 1164.9308703091049, (17, 22968): 1158.1217437397868, (17, 22970): 1162.9522308866713, (17, 22974): 1157.9028570457845, (17, 22980): 1169.148147414584, (17, 23025): 1154.7656475689337, (17, 23028): 1149.5833182495278, (17, 23081): 1153.6987383915957, (17, 23104): 1114.1544222692294, (17, 23147): 1047.054932060142, (17, 23298): 1569.5499537288395, (17, 23376): 1550.312067446606, (17, 23381): 1540.582542811865, (17, 23529): 1583.221696644675, (17, 23556): 1571.8800767850846, (17, 23718): 1556.4200427021115, (17, 24001): 1683.1767649444625, (17, 24094): 1721.6721204282392, (17, 24129): 1740.7581504416612, (17, 24174): 1702.4766899545893, (17, 24235): 1745.769988853572, (17, 24259): 1763.0621629601228, (17, 24260): 1761.8347103694643, (17, 24261): 1757.6117140486954, (17, 24305): 1784.4506446892779, (17, 24306): 1788.319812077562, (17, 24307): 1782.6563008036248, (17, 24308): 1728.9542539759689, (17, 24498): 1829.9974907040885, (17, 24499): 1830.4763447732414, (17, 24500): 1826.879454094112, (17, 24668): 1799.7988607663738, (17, 24711): 1855.42047864048, (17, 24756): 1869.751760683564, (17, 24788): 1874.5592526756914, (17, 24809): 1854.9679375898152, (17, 24813): 1860.9219709133758, (17, 24821): 1858.8927179843097, (17, 24825): 1860.7082386388126, (17, 24832): 1853.3915526960334, (17, 24833): 1856.5564845975841, (17, 24835): 1859.8050736202943, (17, 24837): 1864.6175697113692, (17, 24840): 1853.018479389767, (17, 24841): 1857.6672021491038, (17, 24844): 1853.3215312426994, (17, 24845): 1855.5859322573253, (17, 24846): 1856.1834685976396, (17, 24849): 1857.9843409554578, (17, 24850): 1862.0805775202084, (17, 24863): 1816.9176239251233, (17, 24866): 1822.5129863284476, (17, 24885): 1829.7502518750955, (17, 24886): 1830.5894166154708, (17, 24889): 1841.7286830579435, (17, 24903): 1845.9810712684578, (17, 24909): 1824.5108704185072, (17, 24999): 2066.0699541353624, (17, 25019): 2058.2712279608854, (17, 25028): 2062.9979241011984, (17, 25137): 1621.482521956075, (17, 25145): 1628.8103320046835, (17, 25208): 1718.8246792815185, (17, 25233): 1709.0960306331351, (17, 25371): 1618.4902442849757, (17, 25377): 1596.490247146228, (17, 25828): 1216.0282055015896, (17, 25851): 1154.4260000387596, (17, 25874): 1210.3865266105568, (17, 25898): 1239.1052613737672, (17, 25946): 1209.8965726558065, (17, 26047): 1338.2487919919502, (17, 26066): 1457.820905166186, (17, 26197): 1376.854980663351, (17, 26212): 1053.179352352329, (17, 26253): 1037.803433996686, (17, 26254): 1042.7456630347458, (17, 26257): 1050.9950353708878, (17, 26258): 1041.7194376612438, (17, 26260): 1046.269771410864, (17, 26266): 1033.83024876065, (17, 26267): 1040.265131430112, (17, 26271): 1041.2550634906827, (17, 26304): 1094.4090304123451, (17, 26305): 1092.057379692889, (17, 26363): 1203.0430469695755, (17, 26441): 766.6503714495715, (17, 26442): 764.1295214607356, (17, 26450): 767.8462395798387, (17, 26459): 781.1189200088512, (17, 26462): 786.3659070057473, (17, 26467): 778.561208974405, (17, 26471): 773.9752693914929, (17, 26472): 772.2578396409891, (17, 26473): 770.4663529659681, (17, 26476): 752.4099000540673, (17, 26485): 773.1872718516331, (17, 26493): 766.3875209124759, (17, 26524): 790.9375955292157, (17, 26525): 787.6927052144661, (17, 26556): 775.6605014413569, (17, 26560): 786.8757540783214, (17, 26561): 791.0958750050922, (17, 26564): 773.4014546032158, (17, 26569): 787.9140691755831, (17, 26570): 784.4549928917012, (17, 26573): 778.1854466641917, (17, 26581): 773.0784383646189, (17, 26583): 776.9094809029033, (17, 26593): 766.5113131877613, (17, 26837): 772.7371126120472, (17, 26844): 773.5797845538362, (17, 26863): 759.077809340669, (17, 26893): 755.9939550575108, (17, 26902): 756.7760836130548, (17, 26905): 767.5185208398973, (17, 26912): 764.4860232880483, (17, 26921): 758.3242219629645, (17, 26922): 739.3752025686724, (17, 27212): 1034.377128293152, (17, 27218): 1044.266106874592, (17, 27239): 1033.8411266171952, (17, 27257): 1029.0152773508585, (17, 27274): 1032.032840221803, (17, 27279): 1027.53563719159, (17, 27282): 1026.7167246676004, (17, 27283): 1035.3131957976977, (17, 27285): 1029.8758066923933, (17, 27286): 1021.6298226494853, (17, 27290): 1025.3666873940522, (17, 27295): 1031.2669061006152, (17, 27300): 1033.8697898788153, (17, 27344): 1012.5193198842077, (17, 27366): 1009.1472634914945, (17, 27383): 1020.9875713588625, (17, 27398): 1032.5676923992153, (17, 27406): 1034.7372035210303, (17, 27407): 1038.436274409369, (17, 27426): 1066.0197719875791, (17, 27432): 1053.7233057280691, (17, 27460): 1065.1722037350057, (17, 27523): 942.3017461062057, (17, 27545): 1041.4164264947551, (17, 27602): 1064.1854148940731, (17, 27606): 1070.5527324051923, (17, 27646): 938.5552437785341, (17, 27667): 942.6945665886819, (17, 27672): 946.2606763969378, (17, 27674): 943.3946491349317, (17, 27688): 957.1180839044316, (17, 27692): 943.3242596773267, (17, 27693): 941.8896911741375, (17, 27705): 938.0799354167879, (17, 27712): 935.5931013356251, (17, 27786): 1194.813318938874, (17, 27790): 1231.333318573413, (17, 27791): 1237.009653875445, (17, 27795): 1187.7012773716488, (17, 27801): 1211.0901276018383, (17, 27813): 1191.7202319702876, (17, 27816): 1198.1531756585466, (17, 27823): 1212.3666917983026, (17, 27830): 1205.4735453003807, (17, 27884): 896.3340395666416, (17, 27885): 931.3387652304451, (17, 27896): 911.8853706290357, (17, 27919): 914.1598336160367, (17, 27922): 913.1197805623734, (17, 27930): 906.1548757779155, (17, 27934): 904.2276097620086, (17, 27935): 901.4918942128397, (17, 27948): 889.3969895405936, (17, 27951): 948.4822767029286, (17, 28061): 424.21213222163937, (17, 28290): 660.9092586564743, (17, 28292): 652.2941835035596, (17, 28293): 658.061392945199, (17, 28295): 646.4747142818453, (17, 28296): 655.7127782096798, (17, 28297): 664.5632744495277, (17, 28302): 654.242274550456, (17, 28310): 437.8202688236024, (17, 28313): 449.9854276620297, (17, 28372): 439.5159046629573, (17, 28398): 440.89487318392304, (17, 28399): 439.0796446016123, (17, 28400): 443.39190102637326, (17, 28401): 430.7590779087648, (17, 28445): 450.3768359763661, (17, 28475): 415.5600070627782, (17, 28885): 1746.5516610443015, (17, 28886): 1742.9104843093753, (17, 28915): 1745.9887750352368, (17, 28916): 1742.9363983205865, (17, 28917): 1740.9617610063062, (17, 28921): 1753.3144816524725, (17, 28931): 1752.3137869499851, (17, 28945): 1734.2683171730416, (17, 28982): 1738.6544911474955, (17, 29219): 1759.4908164535482, (17, 29228): 1743.222775412188, (17, 29246): 1849.0571350708374, (17, 29248): 1847.7527027377914, (17, 29282): 1825.7687558059622, (17, 29290): 1859.660035632451, (17, 29291): 1855.3016705889522, (17, 29292): 1859.4027665796475, (17, 29293): 1850.8222658292163, (17, 29294): 1857.708649056968, (17, 29298): 1851.508401644392, (17, 29299): 1850.8126722045204, (17, 29304): 1842.7128509651643, (17, 29317): 1822.0784540481823, (17, 29323): 1820.472829511689, (17, 29330): 1830.4186413095335, (17, 29331): 1835.3306193389521, (17, 29344): 1761.5801078499926, (17, 29445): 1575.9445454835861, (17, 29724): 1190.0766861177644, (17, 29738): 1192.833633199772, (17, 29745): 1186.8132521917719, (17, 29748): 1198.7673169427778, (17, 29750): 1207.6633747087367, (17, 29759): 1193.7330911378424, (17, 29772): 1204.015092706105, (17, 29781): 1202.0680611669704, (17, 29784): 1195.8451151666845, (17, 29790): 1206.147972514899, (17, 29811): 1204.983946820902, (17, 29817): 1252.0772619154188, (17, 29818): 1250.4263296138042, (17, 29929): 1179.5017255705814, (17, 30039): 1189.3239055350477, (17, 30066): 1150.9643743655454, (17, 30116): 1075.8709468883596, (17, 30238): 975.5897409962021, (17, 30248): 992.0956994870952, (17, 30260): 990.6937752544553, (17, 30545): 1690.4531298805432, (17, 30733): 1514.6203583183863, (17, 30756): 1471.0323438653302, (17, 30921): 1554.460952054211, (17, 31079): 1096.501959500502, (17, 31149): 1074.8671780995219, (17, 31154): 1074.9229413110997, (17, 31160): 1073.5757853058105, (17, 31163): 1072.1666726689978, (17, 31189): 1000.7356358384, (17, 31215): 1004.4222129766663, (17, 31259): 993.4597069988773, (17, 31262): 985.7879316737403, (17, 31430): 1103.4992172737273, (17, 31568): 898.1642659336313, (17, 31751): 1056.5612492094194, (25, 109): 501.29529709826926, (25, 872): 1761.9530279495552, (25, 873): 1770.098084148505, (25, 877): 1767.0154907704477, (25, 879): 1768.2215348434654, (25, 884): 1759.9819031660902, (25, 889): 1765.0998801160845, (25, 891): 1757.2915154142188, (25, 892): 1774.5423580465585, (25, 894): 1773.524164827384, (25, 896): 1765.7233626852085, (25, 903): 1767.2933099531135, (25, 909): 1753.5169379197594, (25, 910): 1756.808897257485, (25, 912): 1751.416266159352, (25, 913): 1745.4623586942726, (25, 916): 1742.9918791490375, (25, 926): 1759.5231436215545, (25, 927): 1756.7975559366537, (25, 948): 1754.3416807635715, (25, 961): 1759.1560566177857, (25, 962): 1760.1017284742359, (25, 963): 1761.1582109214398, (25, 967): 1770.7479602852773, (25, 974): 1766.3247682414874, (25, 998): 1773.9539836782787, (25, 1014): 1952.3000071202157, (25, 1086): 1743.4160306584793, (25, 1087): 1742.6443563301316, (25, 1089): 1735.017637937325, (25, 1090): 1738.4202776908357, (25, 1092): 1750.1266459682447, (25, 1097): 1741.1487423647943, (25, 1107): 1756.111280462047, (25, 1387): 558.0519682773619, (25, 1554): 436.6419300720105, (25, 1827): 2134.8429199342418, (25, 1828): 2135.708754728926, (25, 1829): 2136.968972727484, (25, 1830): 2135.6946035002197, (25, 1831): 2136.425141547727, (25, 1832): 2135.5402969759816, (25, 1833): 2135.635080038402, (25, 1836): 2134.6856089454277, (25, 1841): 2139.944178151314, (25, 1843): 2137.7434438954424, (25, 1844): 2138.727593504852, (25, 1845): 2136.1111604947337, (25, 1847): 2127.6172609031114, (25, 1848): 2130.539099111269, (25, 1849): 2144.239433352835, (25, 1850): 2145.669537223469, (25, 1851): 2132.786817171034, (25, 1852): 2133.0121515715623, (25, 1854): 2134.402790909327, (25, 1856): 2127.214492423452, (25, 1857): 2130.3447819679213, (25, 1858): 2142.900216739447, (25, 1861): 2136.7921668906074, (25, 1866): 2127.0372760126556, (25, 1867): 2140.0876246481066, (25, 1868): 2138.3136129043673, (25, 1870): 2138.4996860069555, (25, 1871): 2139.6808475845005, (25, 1875): 2134.247113167894, (25, 1880): 2129.0357652019484, (25, 1882): 2129.914518420174, (25, 1883): 2145.770627946625, (25, 1889): 2130.5477160043697, (25, 1893): 2137.115061476618, (25, 1894): 2135.0470304277164, (25, 1899): 2128.72019686799, (25, 1900): 2130.2399701678414, (25, 1902): 2140.699534065234, (25, 1905): 2143.3697489210417, (25, 1907): 2132.5169317248465, (25, 1910): 2133.4890464730856, (25, 1917): 2148.9533221401985, (25, 1920): 2132.7090215277476, (25, 1935): 2143.718540152581, (25, 1937): 2145.9914661949474, (25, 1946): 2124.113226338603, (25, 1949): 2126.6493757212424, (25, 1950): 2117.749849848931, (25, 1951): 2122.048712889443, (25, 1952): 2125.29971430118, (25, 1953): 2126.672655024194, (25, 1954): 2124.6637484637695, (25, 1958): 2125.936555685457, (25, 1960): 2130.258275540681, (25, 1968): 2131.9639394613237, (25, 1969): 2144.223582199751, (25, 1974): 2141.018920327023, (25, 1975): 2140.992640343225, (25, 1979): 2134.8489935226494, (25, 1980): 2134.393976982765, (25, 1981): 2136.1678012497327, (25, 1985): 2137.6358191132335, (25, 1994): 2114.3555686234727, (25, 2011): 2129.818956622476, (25, 2019): 2151.294258831777, (25, 2020): 2148.4537497230385, (25, 2029): 2137.7169559283966, (25, 2030): 2146.484332486021, (25, 2032): 2135.9867147089794, (25, 2033): 2141.665445058274, (25, 2034): 2141.5911257598405, (25, 2036): 2130.9578488043917, (25, 2037): 2133.67365983508, (25, 2038): 2134.480320859719, (25, 2042): 2167.151265521126, (25, 2050): 2140.16018934593, (25, 2051): 2139.713840515917, (25, 2053): 2140.5698264408725, (25, 2054): 2143.461089489317, (25, 2066): 2137.5818200163753, (25, 2067): 2137.5879149448347, (25, 2071): 2108.895717588051, (25, 2072): 2114.2917500585213, (25, 2073): 2099.3822494892956, (25, 2074): 2098.6620815214587, (25, 2080): 2089.5551641756792, (25, 2082): 2117.206910700877, (25, 2083): 2119.9957649569833, (25, 2089): 2114.038079749965, (25, 2090): 2116.635756857238, (25, 2092): 2113.059721200914, (25, 2098): 2093.0218925746067, (25, 2099): 2096.189185060411, (25, 2101): 2092.476164361136, (25, 2102): 2107.211196143653, (25, 2103): 2102.5882968203796, (25, 2104): 2100.0722699589423, (25, 2106): 2121.8972939436526, (25, 2112): 2094.459202166051, (25, 2113): 2109.324326040647, (25, 2114): 2112.922157156802, (25, 2117): 2124.133642314513, (25, 2123): 2101.9468836945007, (25, 2124): 2104.9856443175136, (25, 2134): 2096.3532625323696, (25, 2138): 2105.2831533977806, (25, 2141): 2097.3976060569175, (25, 2148): 2101.9902440064784, (25, 2150): 2090.0069902895957, (25, 2151): 2093.2137430323496, (25, 2152): 2088.33470975031, (25, 2153): 2102.998624057037, (25, 2154): 2090.3977808537284, (25, 2155): 2088.9791127588196, (25, 2156): 2086.6143764640697, (25, 2157): 2089.93425435619, (25, 2160): 2109.5928711204688, (25, 2161): 2087.8228007163148, (25, 2162): 2103.6018572885414, (25, 2163): 2099.3263336391065, (25, 2164): 2099.053316913944, (25, 2168): 2091.3052521923305, (25, 2172): 2094.2235994171456, (25, 2174): 2092.8621131257387, (25, 2178): 2096.743750996926, (25, 2179): 2094.786172694645, (25, 2183): 2105.088865559887, (25, 2185): 2105.2880085339652, (25, 2186): 2102.858271210117, (25, 2190): 2110.1723973860117, (25, 2192): 2105.7995212848905, (25, 2193): 2105.9365773192726, (25, 2194): 2101.470808614403, (25, 2195): 2100.841288729764, (25, 2197): 2106.766658144661, (25, 2205): 2100.5452305161716, (25, 2207): 2092.444102778786, (25, 2208): 2096.9794287603427, (25, 2212): 2107.208766456216, (25, 2214): 2017.4223404552765, (25, 2225): 2028.2162302581226, (25, 2231): 2006.7646994749969, (25, 2278): 2072.9033580954865, (25, 2284): 2082.1639778738736, (25, 2285): 2080.906422253643, (25, 2291): 2062.8425375656993, (25, 2292): 2064.6046958065276, (25, 2307): 2076.1922288738947, (25, 2313): 2060.7608538128393, (25, 2317): 2057.7323466618964, (25, 2319): 2067.789119744318, (25, 2321): 2072.046863192564, (25, 2323): 2071.431544266527, (25, 2326): 2087.4110106003227, (25, 2327): 2083.429922375167, (25, 2329): 2080.71787043666, (25, 2330): 2077.640411046959, (25, 2332): 2084.22402483178, (25, 2344): 2073.9986520192856, (25, 2346): 2073.8470887485805, (25, 2361): 2072.0643407137945, (25, 2368): 2118.6166005216432, (25, 2374): 2123.0233519140843, (25, 2375): 2124.4728137256043, (25, 2377): 2109.151857525818, (25, 2378): 2127.2470530656924, (25, 2379): 2127.666226288509, (25, 2380): 2129.153367810446, (25, 2383): 2113.2149187881573, (25, 2385): 2115.5667844951267, (25, 2395): 2115.8045965418546, (25, 2397): 2125.862369464661, (25, 2398): 2104.2747188129565, (25, 2399): 2109.7659376631095, (25, 2400): 2108.5309572794195, (25, 2402): 2117.3560600430565, (25, 2403): 2120.778847019088, (25, 2404): 2121.647643580815, (25, 2405): 2113.4106796521355, (25, 2407): 2120.102543863709, (25, 2408): 2124.132194076984, (25, 2409): 2115.904403689567, (25, 2411): 2120.807571938778, (25, 2412): 2119.8887811046247, (25, 2413): 2122.704707476547, (25, 2414): 2118.146019260978, (25, 2422): 2119.7844325143233, (25, 2424): 2120.8434479337507, (25, 2426): 2121.574480397151, (25, 2433): 2115.214488142346, (25, 2436): 2113.551631565786, (25, 2437): 2093.555910516104, (25, 2440): 2097.953483444194, (25, 2445): 2186.73672060827, (25, 2447): 2175.8157396669844, (25, 2454): 2186.0569514451927, (25, 2455): 2186.595580566724, (25, 2460): 2154.835838783538, (25, 2461): 2158.7622437007526, (25, 2471): 2222.4069714037214, (25, 2492): 2156.815481913076, (25, 2511): 2124.571796727463, (25, 2523): 2141.0622417582717, (25, 2525): 2136.365024843104, (25, 2535): 2143.7612888977696, (25, 2537): 2136.7447291601375, (25, 2538): 2141.559095067967, (25, 2539): 2139.643586597391, (25, 2540): 2146.9478795228747, (25, 2542): 2152.0761118088317, (25, 2559): 2251.815315854046, (25, 2575): 2242.9119144536317, (25, 2599): 2091.329936924653, (25, 2600): 2125.237902673384, (25, 2607): 2105.616128731615, (25, 2627): 2145.02363812594, (25, 2647): 2163.8636627074106, (25, 2674): 2153.99090486627, (25, 2681): 2151.532592223025, (25, 2683): 2160.57532541217, (25, 2686): 2150.056786162488, (25, 2689): 2271.65170469066, (25, 2690): 2272.279423080875, (25, 2713): 2297.1415737850075, (25, 2714): 2299.408361102459, (25, 2715): 2302.3896064631267, (25, 2739): 2299.67925572538, (25, 2740): 2280.2733432166738, (25, 2741): 2281.716121827231, (25, 2749): 2295.800771398423, (25, 2750): 2296.651619103365, (25, 2752): 2298.7412128186297, (25, 2755): 2301.1507143915196, (25, 2758): 2300.5311513747056, (25, 2759): 2300.5045827850445, (25, 2769): 2296.947253814344, (25, 2771): 2285.23974604086, (25, 2779): 2286.742107641556, (25, 2784): 2253.3987258070633, (25, 2800): 2260.0420057284814, (25, 2802): 2274.7902899714645, (25, 2803): 2273.583368841405, (25, 2804): 2271.5602882883286, (25, 2805): 2277.5249872687677, (25, 2807): 2277.2640682492856, (25, 2809): 2276.3199440473713, (25, 2812): 2256.964779942106, (25, 2814): 2275.8289761299843, (25, 2817): 2277.236425619908, (25, 2819): 2277.47417260979, (25, 2823): 2259.493105195824, (25, 2832): 2281.3425781966585, (25, 2836): 2267.8801688887384, (25, 2839): 2277.146167679508, (25, 2841): 2277.514272688865, (25, 2843): 2276.381332358887, (25, 2846): 2270.8480881095516, (25, 2849): 2283.571811279513, (25, 2852): 2280.465525679924, (25, 2853): 2285.0064442522475, (25, 2876): 2286.7345470117793, (25, 2877): 2297.5898961460102, (25, 2885): 2301.653310191381, (25, 2918): 2278.5461215310224, (25, 2921): 2283.2769605653248, (25, 2925): 2260.8613089927294, (25, 2926): 2253.2657806033567, (25, 2930): 2270.790827263797, (25, 2931): 2263.055835204043, (25, 2938): 2278.7285748284526, (25, 2940): 2291.660361426068, (25, 2947): 2275.6395826764547, (25, 2949): 2270.370792545069, (25, 2950): 2272.582820361674, (25, 2952): 2270.2914308167683, (25, 2958): 2269.7934159615183, (25, 2959): 2271.864966187267, (25, 2960): 2277.0238253405023, (25, 2961): 2274.6252394327307, (25, 2963): 2267.9205462719783, (25, 2968): 2269.4550975895845, (25, 2976): 2267.235122306022, (25, 2981): 2224.5312795157156, (25, 2982): 2223.4416500229827, (25, 2984): 2221.2121769166592, (25, 3003): 2217.417233436353, (25, 3046): 2185.913896894498, (25, 3050): 2210.061799386991, (25, 3051): 2211.796111465032, (25, 3053): 2206.856573265862, (25, 3069): 2235.0999771310085, (25, 3071): 2205.293971628395, (25, 3080): 2302.03017391674, (25, 3199): 2211.1474534983213, (25, 3200): 2206.003033093595, (25, 3205): 2238.425023706423, (25, 3209): 2208.783994772851, (25, 3215): 2206.2172731368614, (25, 3217): 2199.749438152514, (25, 3249): 2206.688354280089, (25, 3263): 2255.48086554009, (25, 3289): 2221.80526139733, (25, 3301): 2223.6451910014816, (25, 3302): 2221.2080720130643, (25, 3307): 2218.2732426036505, (25, 3310): 2226.4299148333903, (25, 3391): 2238.977007770795, (25, 3509): 1172.6311894776188, (25, 3510): 1167.9857525733028, (25, 3511): 1170.963003006351, (25, 3512): 1167.9897707663592, (25, 3514): 1168.8781569091364, (25, 3519): 1184.1447004679303, (25, 3536): 1180.6232732505528, (25, 3545): 1187.8005488004587, (25, 3548): 1180.5366963115741, (25, 3572): 1183.4004231318065, (25, 3581): 1178.179551125569, (25, 3583): 1174.5196650672249, (25, 3601): 1193.0808941271089, (25, 3656): 1186.1012527767316, (25, 3669): 1178.4009184690194, (25, 3670): 1182.6296753190918, (25, 3695): 1158.21990751571, (25, 3696): 1161.4862242009176, (25, 3782): 1180.8711743957158, (25, 3792): 1175.9101045918103, (25, 3989): 827.448717926441, (25, 4008): 852.900017650955, (25, 4031): 852.5870776255373, (25, 4045): 842.2720750892427, (25, 4144): 842.5754714152833, (25, 4145): 816.1672652800298, (25, 4164): 832.5217827636959, (25, 4168): 824.1641570122664, (25, 4173): 822.3470353756358, (25, 4181): 806.9155077869648, (25, 4228): 793.2510473766548, (25, 4248): 785.74491548309, (25, 4254): 649.4971101681948, (25, 4260): 649.5937634748534, (25, 4262): 658.5150404015847, (25, 4273): 656.3918604238852, (25, 4319): 578.5371387835016, (25, 4326): 575.7001285564564, (25, 4328): 576.4936271804637, (25, 4334): 582.1524539454632, (25, 4335): 580.4163484065947, (25, 4372): 834.0045973029378, (25, 4413): 916.966227978475, (25, 4434): 827.6564014416705, (25, 4447): 826.7945505799414, (25, 4452): 830.27030607648, (25, 4463): 766.2182907523678, (25, 4465): 765.740255852717, (25, 4619): 956.6801446596711, (25, 4645): 964.2770233904712, (25, 4657): 966.2297150380164, (25, 4666): 964.9153272801053, (25, 4676): 973.5246853203636, (25, 4678): 973.5991009885539, (25, 4689): 972.385416833385, (25, 4704): 1016.5038978282602, (25, 4726): 1203.3784990908653, (25, 4727): 1200.2800339600153, (25, 4730): 1194.033961552316, (25, 4731): 1197.3844047511975, (25, 4734): 1191.8963282056322, (25, 4735): 1190.2910892980244, (25, 4736): 1192.9301978851454, (25, 4737): 1189.2971147555284, (25, 4738): 1190.9309477342435, (25, 4756): 1194.742351467445, (25, 4760): 1172.6655052463857, (25, 4761): 1171.8115049163628, (25, 4762): 1170.014197809859, (25, 4765): 1174.9730524697352, (25, 4773): 1208.1815828174576, (25, 4774): 1207.5166982500768, (25, 4790): 1205.8098736035422, (25, 4795): 1202.5801585607903, (25, 4799): 1209.9673585292712, (25, 4801): 1219.324243266235, (25, 4804): 1201.0156534488378, (25, 4805): 1198.393208067166, (25, 4806): 1209.4420309755224, (25, 4815): 1208.3319106205865, (25, 4816): 1215.1219817564672, (25, 4817): 1219.079799288954, (25, 4826): 1213.7201143318985, (25, 4830): 1210.3643757369916, (25, 4839): 1181.8100581287533, (25, 4840): 1185.6100941655036, (25, 4841): 1179.9291586582126, (25, 4846): 1177.3736708268407, (25, 4848): 1178.7643452690545, (25, 4850): 1181.9339038409414, (25, 4871): 1136.4347434154224, (25, 4883): 1166.1381101252352, (25, 4900): 1147.9355961474926, (25, 4901): 1145.7449162793173, (25, 4917): 1000.0009844272412, (25, 4931): 980.6578884148302, (25, 4944): 1000.4945487993941, (25, 4956): 985.9162198685668, (25, 4958): 988.7625357047309, (25, 4959): 987.4491169662504, (25, 4961): 988.4414985223318, (25, 4966): 983.1772437794601, (25, 5207): 962.2403176972739, (25, 5272): 475.29650889253, (25, 5283): 483.57653164424056, (25, 5287): 506.446700054672, (25, 5289): 510.4202648492556, (25, 5293): 467.32115849123045, (25, 5295): 489.3038123387294, (25, 5296): 494.9240650704371, (25, 5298): 497.90828114662673, (25, 5303): 509.3405794057061, (25, 5305): 482.49961782608193, (25, 5306): 485.2165785717732, (25, 5307): 479.0134637665287, (25, 5308): 488.0335903219415, (25, 5313): 480.06976691520595, (25, 5314): 482.70941286882345, (25, 5317): 492.0607671704073, (25, 5319): 503.2658803576329, (25, 5324): 494.3725175289827, (25, 5326): 488.305353027041, (25, 5348): 488.7898505405509, (25, 5351): 503.15656143657964, (25, 5399): 523.4664971331632, (25, 5413): 526.6282579111978, (25, 5422): 521.7294939414699, (25, 5445): 506.8490279744716, (25, 5448): 499.67902997507156, (25, 5456): 504.4484346907709, (25, 5467): 512.7837213533005, (25, 5624): 413.6001098239403, (25, 5671): 583.6393122313697, (25, 5672): 572.4256799007369, (25, 5797): 713.2207543270486, (25, 5871): 679.0749361355394, (25, 5976): 599.7572544728426, (25, 6118): 1750.3567916950499, (25, 6248): 1858.3981040025167, (25, 6345): 222.13454017245044, (25, 6352): 242.16214339872937, (25, 6354): 215.24644458473708, (25, 6359): 215.13883843272325, (25, 6376): 247.77533632954595, (25, 6378): 218.0019376701478, (25, 6381): 219.34528572596346, (25, 6383): 224.86890960628008, (25, 6396): 236.64908170100873, (25, 6399): 226.3657348307021, (25, 6408): 237.88301800774707, (25, 6409): 218.95958372690143, (25, 6419): 239.40824323637912, (25, 6422): 227.90620111842745, (25, 6423): 229.06229895926714, (25, 6424): 206.3074830790541, (25, 6439): 207.13496353966815, (25, 6464): 209.90559840930302, (25, 6465): 215.12518460111005, (25, 6469): 219.37697268068274, (25, 6470): 222.20089489468498, (25, 6472): 210.13591962288825, (25, 6480): 197.60146248585568, (25, 6486): 168.66410400088594, (25, 6497): 177.540767776965, (25, 6503): 190.4959323338225, (25, 6508): 198.64539635494117, (25, 6509): 190.13338334085913, (25, 6521): 187.87128560736662, (25, 6544): 179.33667460410354, (25, 6552): 208.2590584868691, (25, 6553): 210.58464510734575, (25, 6554): 213.09960723478386, (25, 6578): 205.80721309703688, (25, 6582): 198.08938319019208, (25, 6601): 202.66889989185447, (25, 6609): 194.4322039829795, (25, 6610): 191.479246612742, (25, 6611): 197.04237478741823, (25, 6614): 201.8146482160752, (25, 6615): 199.2944673188349, (25, 6616): 189.1092462799043, (25, 6617): 192.9004719157687, (25, 6618): 181.6231641200976, (25, 6619): 202.23420287358874, (25, 6620): 185.33332679547797, (25, 6621): 186.5657210629967, (25, 6622): 188.65686193666997, (25, 6623): 197.9312197805515, (25, 6624): 195.79804227234916, (25, 6625): 198.15910106958964, (25, 6626): 203.9743185826914, (25, 6627): 205.5765431710883, (25, 6628): 181.98109911086095, (25, 6629): 190.7340456820935, (25, 6630): 205.78481665046698, (25, 6632): 192.97472930274503, (25, 6634): 205.56263636078197, (25, 6635): 189.27412360791195, (25, 6636): 187.70551480835732, (25, 6637): 193.12700239283305, (25, 6638): 202.02365716777965, (25, 6639): 203.17978444096286, (25, 6640): 203.56132754591474, (25, 6641): 183.74640487635918, (25, 6642): 199.52662051421402, (25, 6643): 206.86138856708894, (25, 6645): 200.26691809673986, (25, 6646): 185.27252086713537, (25, 6647): 200.2878682120906, (25, 6653): 200.539017729564, (25, 6655): 204.38231065371156, (25, 6658): 204.28199536739217, (25, 6662): 197.02389711651185, (25, 6819): 305.13092293387314, (25, 6996): 227.09486988593767, (25, 7059): 189.05312688619057, (25, 7187): 264.6514371766633, (25, 7304): 329.84653310280333, (25, 7528): 223.8083161758711, (25, 7720): 22.607963871432357, (25, 7793): 2.5295588396545314, (25, 7807): 6.439069852707247, (25, 7808): 8.178712768328502, (25, 7831): 154.60723494789053, (25, 7850): 154.85033358846732, (25, 7852): 164.41906202652729, (25, 8012): 58.404426843353505, (25, 8125): 120.79921634418292, (25, 8208): 76.39652847105675, (25, 8392): 79.4479109938792, (25, 8651): 482.6418632205613, (25, 9088): 360.9891642923898, (25, 9443): 556.6532723093745, (25, 9444): 551.769755031169, (25, 9828): 738.8818585256322, (25, 9868): 729.0143199322445, (25, 10180): 133.2139320963076, (25, 10256): 200.1093196472951, (25, 10276): 147.872339306582, (25, 10378): 112.19499965738987, (25, 10676): 225.64968642540043, (25, 10714): 252.43873145206896, (25, 10730): 178.52893817356795, (25, 10862): 842.3374348975287, (25, 10881): 846.6057628321176, (25, 10883): 848.4046308606988, (25, 10885): 840.8730931895116, (25, 10891): 851.277905214697, (25, 10909): 845.4602466668721, (25, 10911): 840.4761082107004, (25, 10913): 841.2858108542605, (25, 10915): 838.3573122770465, (25, 10919): 836.5353698975689, (25, 11037): 882.2728095545377, (25, 11039): 851.1545031404131, (25, 11516): 1119.4885501541273, (25, 11856): 584.5405346863233, (25, 11857): 581.4999041622507, (25, 11861): 583.146563716974, (25, 11881): 578.3753127951508, (25, 11902): 561.3744334894141, (25, 11911): 558.0054728719421, (25, 11914): 560.4749916314623, (25, 11922): 573.2157943033679, (25, 11924): 577.1426756071692, (25, 11926): 572.2281723031333, (25, 11950): 581.6684794518859, (25, 11963): 597.6879726079129, (25, 11983): 586.7014528135273, (25, 11985): 605.7444713149368, (25, 12009): 602.4132161871713, (25, 12010): 591.0874270209948, (25, 12018): 592.9467585108528, (25, 12020): 596.0383036780216, (25, 12021): 597.9072878948482, (25, 12024): 608.7514793638329, (25, 12025): 605.1118826238106, (25, 12027): 602.5354515844185, (25, 12031): 589.189953289811, (25, 12032): 592.9835120365788, (25, 12035): 601.6894237787102, (25, 12041): 607.3883223362316, (25, 12045): 456.22311725843474, (25, 12145): 525.8377172290049, (25, 12275): 841.7997454188543, (25, 12294): 818.0740393622243, (25, 12358): 907.5472610750907, (25, 12463): 944.9286558882817, (25, 12465): 944.1918049223625, (25, 12482): 955.0914198065599, (25, 12503): 953.9532848688834, (25, 12506): 957.8207835375658, (25, 12549): 945.3192757372334, (25, 12559): 943.1624306958801, (25, 12569): 947.7975866757826, (25, 12572): 950.6264960429163, (25, 12574): 944.2580302313147, (25, 12576): 948.218831622494, (25, 12591): 945.2935815210799, (25, 12608): 967.4570469849591, (25, 12696): 928.0593786034912, (25, 12710): 947.6973723304696, (25, 12728): 939.6426198024434, (25, 12766): 343.5020098663806, (25, 12771): 295.4803257141811, (25, 12790): 293.4409052591274, (25, 12795): 292.322095050162, (25, 12797): 247.70895744055505, (25, 12798): 250.36038838954977, (25, 12811): 274.9668449199936, (25, 12830): 271.6492076777939, (25, 12848): 265.7936989434755, (25, 12850): 262.0223110659615, (25, 12852): 267.3861838657465, (25, 12854): 263.72226164465434, (25, 12859): 267.02344827501, (25, 12861): 251.94527524657013, (25, 12865): 284.03538615417864, (25, 12866): 279.1353257548843, (25, 12867): 289.4216640527289, (25, 12874): 284.83483819792093, (25, 12875): 286.4921652072669, (25, 12881): 278.1385647858409, (25, 12883): 282.40934128950477, (25, 12885): 289.68468079039263, (25, 12888): 278.29426826819747, (25, 12889): 275.3033168225565, (25, 12892): 286.7782995673098, (25, 12893): 280.5143612316237, (25, 12896): 280.67573656881785, (25, 12906): 294.1347583774447, (25, 13018): 324.98517916380075, (25, 13071): 339.55591303195354, (25, 13131): 262.03485595713346, (25, 13146): 267.9637001396846, (25, 13159): 322.01077377940015, (25, 13193): 254.67910775252938, (25, 13198): 206.68134262615996, (25, 13292): 227.75414540538122, (25, 13296): 214.9654575533009, (25, 13406): 244.84727518445982, (25, 13407): 248.29984350955252, (25, 13417): 276.73589088108935, (25, 13418): 281.89903874998146, (25, 13438): 262.78561651235106, (25, 13442): 254.2492683838443, (25, 13443): 254.54964805263376, (25, 13764): 598.1975744691981, (25, 13766): 593.7301094883514, (25, 13771): 606.1729583904319, (25, 13783): 588.6544343522825, (25, 13784): 585.3792018301797, (25, 13792): 626.9185507693788, (25, 13824): 593.379900153553, (25, 14017): 520.6302265526266, (25, 14870): 725.3694519205823, (25, 14997): 294.6783243180879, (25, 15000): 295.665209140269, (25, 15003): 293.60015793971854, (25, 15006): 278.363301905866, (25, 15007): 274.64004021661907, (25, 15056): 279.7727548539163, (25, 15063): 284.1367906102553, (25, 15069): 287.4212460318068, (25, 15076): 275.0430993018259, (25, 15086): 285.4609349570734, (25, 15087): 291.45506016524365, (25, 15111): 301.8956254468919, (25, 15116): 295.9880793031411, (25, 15722): 400.4739730999354, (25, 15998): 506.00590059916755, (25, 16073): 1424.1589481585986, (25, 16939): 1876.412658297563, (25, 16940): 1870.3655301564618, (25, 16951): 1877.368732786213, (25, 16963): 1877.9193715139886, (25, 16965): 1885.228095279245, (25, 16969): 1883.5192259239311, (25, 16970): 1880.5416511724954, (25, 16971): 1873.9515999882983, (25, 16973): 1873.5553727302329, (25, 16974): 1888.20885947608, (25, 16976): 1881.0252405554402, (25, 16978): 1876.1950290322898, (25, 16980): 1883.4260133303662, (25, 16982): 1888.2062142440373, (25, 17045): 2099.1686391417375, (25, 17048): 2107.699778729461, (25, 17304): 748.6577791050291, (25, 17305): 745.0642450069158, (25, 17330): 748.8726901615078, (25, 17334): 740.3188272533496, (25, 17343): 755.1813051877108, (25, 17345): 740.6625969788302, (25, 17347): 748.7734604237982, (25, 17351): 729.1314922852337, (25, 17372): 739.6302900737918, (25, 17373): 754.5908418531458, (25, 17377): 755.6993891466549, (25, 17382): 746.0932156723507, (25, 17383): 747.6535194137538, (25, 17389): 742.0388283809115, (25, 17400): 751.7070054435151, (25, 17401): 751.4144856425571, (25, 17402): 752.3379514347253, (25, 17403): 753.3493330937, (25, 17440): 742.0852774834062, (25, 17455): 753.9900763524895, (25, 17491): 755.5180419098231, (25, 17507): 733.5598308179714, (25, 17509): 738.8003900104987, (25, 17590): 726.2953821452188, (25, 17615): 694.9529270134599, (25, 17642): 700.1984292675538, (25, 17643): 699.7106259283338, (25, 17668): 694.7847666724449, (25, 17721): 683.1384047313998, (25, 17754): 733.2745150929018, (25, 17769): 735.0870741348938, (25, 17776): 714.3763432760496, (25, 17804): 743.6899387911599, (25, 17809): 749.0186928890657, (25, 17824): 745.5014262898076, (25, 17837): 730.6721017350984, (25, 17838): 731.4952673714274, (25, 17862): 727.6580498774409, (25, 17866): 738.8813384576667, (25, 17872): 723.6656975954047, (25, 17873): 715.1500972883541, (25, 17881): 728.2577786765727, (25, 17947): 1383.2491746289465, (25, 17951): 1371.8085742504422, (25, 17953): 1369.6172400918554, (25, 17954): 1370.4156261613043, (25, 17959): 1380.9086298086304, (25, 17963): 1376.901562470248, (25, 18000): 1318.7669324355213, (25, 18001): 1321.0178700541437, (25, 18111): 1487.691727593165, (25, 18148): 1194.2434164115325, (25, 18166): 1308.8311450576455, (25, 18189): 1413.5734420513604, (25, 18239): 757.0540454943336, (25, 18240): 757.0321790586618, (25, 18245): 757.57506092549, (25, 18247): 756.4509488719966, (25, 18251): 757.6069188184171, (25, 18256): 758.9121094529327, (25, 18258): 757.5973446372304, (25, 18259): 757.8641538244093, (25, 18260): 758.4209148515679, (25, 18262): 759.4451153323082, (25, 18263): 759.2901540049668, (25, 18264): 759.8402603440342, (25, 18266): 759.8872780406871, (25, 18267): 760.4213205021513, (25, 18268): 760.7035038052068, (25, 18269): 761.7759668075873, (25, 18275): 761.2699639782779, (25, 18285): 759.6346675641704, (25, 18308): 748.5599529943587, (25, 18313): 744.9256060858473, (25, 18314): 746.6734813839839, (25, 18315): 761.5775765026035, (25, 18316): 761.5584740169276, (25, 18317): 762.0639526362497, (25, 18320): 762.4396358793206, (25, 18321): 762.7481757998083, (25, 18322): 763.5308238953079, (25, 18324): 764.0689345702716, (25, 18325): 766.4051054332604, (25, 18326): 765.5315304226039, (25, 18327): 762.5880676301841, (25, 18329): 767.3784324881049, (25, 18330): 766.4295819401619, (25, 18331): 764.82889817124, (25, 18332): 763.2183830247747, (25, 18333): 766.120740449565, (25, 18336): 764.7050495695819, (25, 18337): 765.4557885408072, (25, 18403): 764.684441644698, (25, 18432): 735.9346829720982, (25, 18451): 755.2645993970638, (25, 18466): 774.5911564370762, (25, 18481): 762.0142994718926, (25, 18483): 762.0586483259443, (25, 18484): 760.7396853282728, (25, 18485): 756.734446395777, (25, 18486): 760.0321840436593, (25, 18487): 757.0061556265074, (25, 18489): 759.8102181354254, (25, 18490): 762.6766164639284, (25, 18491): 764.0804712668712, (25, 18492): 754.0390260677856, (25, 18493): 759.4881173613996, (25, 18494): 759.2738791625467, (25, 18495): 761.6246085083282, (25, 18496): 760.1859694966287, (25, 18497): 756.2768700824805, (25, 18498): 757.1147851472872, (25, 18499): 759.3169944320608, (25, 18501): 757.6530340251053, (25, 18502): 756.2410674867447, (25, 18503): 755.2043862629446, (25, 18504): 760.8181922796812, (25, 18506): 757.756523665201, (25, 18507): 756.3925972144876, (25, 18508): 758.9706158544427, (25, 18509): 758.9610210668725, (25, 18510): 755.1870068399533, (25, 18511): 759.8371750953452, (25, 18512): 758.246206545551, (25, 18515): 760.8922934715325, (25, 18516): 760.8739275132535, (25, 18517): 759.0412156567177, (25, 18518): 762.0685943693101, (25, 18519): 761.1477055839658, (25, 18520): 758.603436971214, (25, 18522): 767.2261217677177, (25, 18523): 767.4780515964301, (25, 18532): 769.3567222694302, (25, 18535): 765.3998615974692, (25, 18537): 763.1972020149441, (25, 18539): 763.6296393088841, (25, 18540): 763.8567800336345, (25, 18541): 764.9176968991961, (25, 18542): 765.5965264368486, (25, 18543): 762.2041513462182, (25, 18546): 763.7281798327896, (25, 18555): 767.1804741851566, (25, 18556): 767.7756919367922, (25, 18565): 769.0299579504147, (25, 18567): 769.9400447763463, (25, 18568): 768.0988951365666, (25, 18577): 781.630020664735, (25, 18583): 779.4952365912857, (25, 18605): 782.5149547824345, (25, 18608): 770.9200919861836, (25, 18616): 795.1229879661362, (25, 18618): 805.7768711263286, (25, 18625): 802.4915902531114, (25, 18645): 793.2052385167876, (25, 18646): 795.5210929762911, (25, 18653): 786.1549067413649, (25, 18654): 794.7862119684744, (25, 18655): 789.0335137384218, (25, 18666): 824.6074544046745, (25, 18837): 802.2468079998401, (25, 18974): 757.6060837045574, (25, 18999): 768.1760119857466, (25, 19000): 771.4053862766324, (25, 19174): 637.357326824952, (25, 19342): 707.0751051306353, (25, 19455): 646.3299765682028, (25, 19555): 506.37412923298723, (25, 19564): 529.5784805475266, (25, 19573): 520.0845740080041, (25, 19586): 514.888941286121, (25, 19605): 514.9222601620394, (25, 19611): 520.7513731657347, (25, 19614): 514.2032667149845, (25, 19641): 594.4124098564794, (25, 19702): 597.1991003031221, (25, 19713): 590.4547375659857, (25, 19731): 462.32548280664037, (25, 19819): 628.5084946366718, (25, 19893): 478.94546166653583, (25, 19899): 525.6444118864817, (25, 19929): 487.93807917722125, (25, 19951): 569.0963396172622, (25, 19962): 500.8014040353453, (25, 19970): 506.27793597315053, (25, 19971): 509.38387256400915, (25, 19972): 504.6066783060971, (25, 19975): 499.4402048031192, (25, 19978): 574.2402918683129, (25, 19987): 573.9677306943502, (25, 19989): 551.798663332186, (25, 20039): 577.2498898057999, (25, 20043): 584.2877068708436, (25, 20047): 575.2917612516891, (25, 20052): 552.547877564567, (25, 20054): 555.5159897394814, (25, 20085): 652.69980464002, (25, 20104): 659.1817312653616, (25, 20132): 621.4577693163255, (25, 20203): 503.9875521057655, (25, 20280): 505.6544295071429, (25, 20285): 507.997289499278, (25, 20290): 507.31078120944153, (25, 20297): 499.2376787910405, (25, 20309): 598.8860658375876, (25, 20453): 694.4124135874337, (25, 20485): 449.5939293904559, (25, 20520): 428.7069045459018, (25, 20526): 433.4635637725355, (25, 20698): 856.0704610131914, (25, 20868): 1039.6514953168137, (25, 21042): 187.02357459644853, (25, 21057): 231.28075382527166, (25, 21066): 208.50187992734112, (25, 21075): 201.85767799927274, (25, 21093): 189.04435524309466, (25, 21098): 219.41321986936688, (25, 21127): 189.86843933718026, (25, 21130): 197.63302505140825, (25, 21144): 197.61913200841445, (25, 21146): 186.99257018520458, (25, 21147): 197.3807647997496, (25, 21148): 204.46659690402817, (25, 21153): 197.21932171862923, (25, 21293): 258.31438112197617, (25, 21426): 279.3361819209403, (25, 21442): 333.4800845858781, (25, 21451): 338.4574577757951, (25, 21466): 303.55688438185445, (25, 21469): 309.1315732334124, (25, 21471): 300.8617620300543, (25, 21473): 304.8360310528481, (25, 21475): 300.5970466519135, (25, 21482): 314.64997662863755, (25, 21484): 312.4388500437556, (25, 21488): 309.7133498372744, (25, 21494): 297.77843547941933, (25, 21498): 302.66473659313425, (25, 21500): 292.79344919479826, (25, 21514): 296.6065375196503, (25, 21537): 285.7404538515488, (25, 21662): 297.1793615065151, (25, 21691): 271.39817998336713, (25, 21757): 247.61814618848024, (25, 21777): 104.7804591372987, (25, 21778): 98.2871188138091, (25, 21779): 103.5750360800776, (25, 21790): 110.83327824629124, (25, 21802): 113.08722770228565, (25, 21824): 121.44950590592505, (25, 21874): 107.64174845025207, (25, 21879): 108.50355634026677, (25, 21983): 125.15303817812278, (25, 22002): 199.74519460164987, (25, 22132): 184.63937964752617, (25, 22261): 826.0820737227742, (25, 22298): 815.7071846391301, (25, 22339): 903.7029725067185, (25, 22508): 693.0169089968206, (25, 22841): 2230.9891374227095, (25, 22842): 2230.9531414096064, (25, 22874): 2214.253359322769, (25, 22941): 2216.173643227927, (25, 22956): 2226.170739927423, (25, 22960): 2229.3029729725786, (25, 22968): 2238.2616629393947, (25, 22970): 2241.160691151063, (25, 22974): 2245.5049379594457, (25, 22980): 2257.579189690167, (25, 23025): 2255.459751478221, (25, 23028): 2252.5752854216335, (25, 23081): 2271.783239841485, (25, 23104): 2248.5275350090815, (25, 23147): 2144.2797078867097, (25, 23298): 402.7405392493449, (25, 23376): 383.06580059943633, (25, 23381): 367.122023837579, (25, 23529): 411.7482935233108, (25, 23556): 400.851199637288, (25, 23718): 395.47526809545866, (25, 24001): 520.1485038745228, (25, 24094): 549.9344381740216, (25, 24129): 569.3975256914282, (25, 24174): 527.5196647912167, (25, 24235): 569.982652569533, (25, 24259): 589.2002382764689, (25, 24260): 587.688264909166, (25, 24261): 583.6383478463788, (25, 24305): 611.7187968625717, (25, 24306): 615.2863981501695, (25, 24307): 609.7371097964669, (25, 24308): 574.7238313170994, (25, 24498): 664.5212856119394, (25, 24499): 664.8342618489163, (25, 24500): 661.3646620292378, (25, 24668): 644.5287755615354, (25, 24711): 686.5965190854297, (25, 24756): 698.4470934366674, (25, 24788): 704.4149124111798, (25, 24809): 682.0405082672127, (25, 24813): 689.0329661645198, (25, 24821): 686.749851411731, (25, 24825): 688.3501025494237, (25, 24832): 680.5965287726228, (25, 24833): 683.9395999057739, (25, 24835): 687.2469017194321, (25, 24837): 692.6313556917135, (25, 24840): 680.0542278432318, (25, 24841): 685.2753662905144, (25, 24844): 680.1752143124132, (25, 24845): 683.3604814567918, (25, 24846): 682.8813056949019, (25, 24849): 684.6867221215191, (25, 24850): 690.0019189020766, (25, 24863): 643.7458741550336, (25, 24866): 649.7362022350808, (25, 24885): 656.7049276827228, (25, 24886): 657.1578847651696, (25, 24889): 670.5904060999128, (25, 24903): 675.8910120733983, (25, 24909): 654.2722059674429, (25, 24999): 922.0799172676319, (25, 25019): 916.6088990712698, (25, 25028): 918.081990407996, (25, 25137): 568.0985615573182, (25, 25145): 573.0615840654729, (25, 25208): 677.9279624061957, (25, 25233): 672.3977982522139, (25, 25371): 538.2681217373074, (25, 25377): 513.9439890059111, (25, 25828): 306.3374093053845, (25, 25851): 274.5484614835786, (25, 25874): 283.54114855202727, (25, 25898): 318.3974986491685, (25, 25946): 303.9159224540416, (25, 26047): 391.90791234325565, (25, 26066): 347.99014932775395, (25, 26197): 343.692548603653, (25, 26212): 445.2669648128539, (25, 26253): 462.4591731395792, (25, 26254): 453.6109923408249, (25, 26257): 454.86271750170965, (25, 26258): 461.06370408889427, (25, 26260): 457.3137285314377, (25, 26266): 447.51425375775165, (25, 26267): 445.5119452164027, (25, 26271): 447.3847140608677, (25, 26304): 381.55386011149903, (25, 26305): 376.4574036848837, (25, 26363): 344.63780867051395, (25, 26441): 897.9817253767047, (25, 26442): 895.3322531130445, (25, 26450): 884.9050292986013, (25, 26459): 886.1967340199075, (25, 26462): 888.6091659550405, (25, 26467): 919.4950932351055, (25, 26471): 909.7637063847689, (25, 26472): 908.5366163449532, (25, 26473): 907.8837578894561, (25, 26476): 899.9573906186054, (25, 26485): 890.3833038733266, (25, 26493): 889.6365344269275, (25, 26524): 894.2146761572822, (25, 26525): 892.4040615275807, (25, 26556): 905.6831657330059, (25, 26560): 906.44538891695, (25, 26561): 900.2011306751641, (25, 26564): 902.3524768125005, (25, 26569): 897.9754766080034, (25, 26570): 894.6309693819575, (25, 26573): 895.3860404892359, (25, 26581): 894.3288014100876, (25, 26583): 892.5245652977093, (25, 26593): 893.3923891592402, (25, 26837): 920.7712292569702, (25, 26844): 928.2138795887513, (25, 26863): 910.0976011308603, (25, 26893): 930.7511396831146, (25, 26902): 940.7897285316354, (25, 26905): 932.3046930286185, (25, 26912): 939.601406485896, (25, 26921): 920.1043509946239, (25, 26922): 897.409687045398, (25, 27212): 1020.779187451793, (25, 27218): 1014.7659859985613, (25, 27239): 1033.989803641745, (25, 27257): 1025.923280183072, (25, 27274): 1036.2731999149796, (25, 27279): 1033.7410008871886, (25, 27282): 1025.6913915356158, (25, 27283): 1030.8117351108403, (25, 27285): 1039.3232292156613, (25, 27286): 1030.2164108229495, (25, 27290): 1018.6484359299541, (25, 27295): 1015.1948786526409, (25, 27300): 1038.0545931127208, (25, 27344): 1012.0166835505667, (25, 27366): 1020.1847721666066, (25, 27383): 1037.9604098380414, (25, 27398): 1050.1884775443225, (25, 27406): 1042.903490326747, (25, 27407): 1046.0778955915798, (25, 27426): 1042.4403852650435, (25, 27432): 1005.6103154102467, (25, 27460): 1029.6417678740427, (25, 27523): 1008.3703723187151, (25, 27545): 1168.118910854719, (25, 27602): 1346.4546481402674, (25, 27606): 1350.7420558191664, (25, 27646): 1143.919288029721, (25, 27667): 1180.3584991048967, (25, 27672): 1182.8317651056366, (25, 27674): 1176.2689889745116, (25, 27688): 1183.7088715421164, (25, 27692): 1188.4967800938464, (25, 27693): 1182.921401492152, (25, 27705): 1182.001281593991, (25, 27712): 1184.2121339419725, (25, 27786): 1378.1285322619476, (25, 27790): 1366.272424428956, (25, 27791): 1365.83129232707, (25, 27795): 1367.1951803797979, (25, 27801): 1357.5315760480928, (25, 27813): 1382.7793312374324, (25, 27816): 1377.8131781059194, (25, 27823): 1357.2484012273342, (25, 27830): 1371.7324814356082, (25, 27884): 1076.4568021139016, (25, 27885): 1127.604354255762, (25, 27896): 1097.034354717371, (25, 27919): 1095.5546788824568, (25, 27922): 1100.988690009319, (25, 27930): 1085.0384636990086, (25, 27934): 1086.4380112155313, (25, 27935): 1087.2472774265839, (25, 27948): 1301.5216609861511, (25, 27951): 1319.7010180331827, (25, 28061): 1085.4481653367995, (25, 28290): 1485.2034959944956, (25, 28292): 1491.912639847412, (25, 28293): 1486.3917148932194, (25, 28295): 1482.0644854460693, (25, 28296): 1484.2998744389806, (25, 28297): 1481.553438303261, (25, 28302): 1477.8339568183785, (25, 28310): 1598.132336281506, (25, 28313): 1604.8487420134743, (25, 28372): 1604.896160337322, (25, 28398): 1605.6050862352017, (25, 28399): 1603.0675886974295, (25, 28400): 1607.3107861187991, (25, 28401): 1596.0529005311646, (25, 28445): 1601.3419172311494, (25, 28475): 1586.912143644749, (25, 28885): 565.9472989910523, (25, 28886): 562.2690641556419, (25, 28915): 565.3570575630334, (25, 28916): 562.2804252968918, (25, 28917): 560.3251331811387, (25, 28921): 572.7656360965346, (25, 28931): 571.7118381901149, (25, 28945): 554.5147487863273, (25, 28982): 558.3031255417477, (25, 29219): 583.9745021945384, (25, 29228): 567.6637196785899, (25, 29246): 678.3271626039239, (25, 29248): 679.0997139615015, (25, 29282): 656.4070365331578, (25, 29290): 687.1045657450919, (25, 29291): 683.2000415674167, (25, 29292): 687.1326248181123, (25, 29293): 678.3942758293642, (25, 29294): 686.1882792784893, (25, 29298): 679.5740876942979, (25, 29299): 679.3678675725885, (25, 29304): 670.0298361282255, (25, 29317): 648.4169977826775, (25, 29323): 646.6862493048675, (25, 29330): 657.1757346472887, (25, 29331): 661.9743568690185, (25, 29344): 589.6133525750035, (25, 29445): 417.9963515394773, (25, 29724): 2202.4938118503323, (25, 29738): 2205.710438213586, (25, 29745): 2196.301496942173, (25, 29748): 2198.0509221659577, (25, 29750): 2203.274083402042, (25, 29759): 2193.6519968318557, (25, 29772): 2205.537896955497, (25, 29781): 2202.9403621478696, (25, 29784): 2200.946681215886, (25, 29790): 2205.512945657375, (25, 29811): 2198.714652511866, (25, 29817): 2220.627990916831, (25, 29818): 2218.1045225388298, (25, 29929): 2195.25914004743, (25, 30039): 2237.7047164558226, (25, 30066): 2210.987442123274, (25, 30116): 2100.974233184784, (25, 30238): 1938.431107594488, (25, 30248): 2018.6740447476038, (25, 30260): 2020.537909487898, (25, 30545): 511.59092114971287, (25, 30733): 339.55528488497134, (25, 30756): 290.3928864909839, (25, 30921): 374.55597999193316, (25, 31079): 337.8788591387044, (25, 31149): 286.5577666999103, (25, 31154): 295.20786846414245, (25, 31160): 285.51794518351534, (25, 31163): 295.3271930621838, (25, 31189): 291.22172105466257, (25, 31215): 298.12839468964603, (25, 31259): 336.0819710226537, (25, 31262): 334.4798140958839, (25, 31430): 365.2038081657736, (25, 31568): 451.2561445078825, (25, 31751): 355.1642155121319, (27, 109): 683.1758602023205, (27, 872): 1228.7820703556924, (27, 873): 1236.8107445432308, (27, 877): 1233.5959438871876, (27, 879): 1234.7684924972443, (27, 884): 1226.2602183402396, (27, 889): 1231.38997766894, (27, 891): 1223.6504027825113, (27, 892): 1241.0385651582296, (27, 894): 1240.1048246009693, (27, 896): 1232.7120834815566, (27, 903): 1233.6745068511275, (27, 909): 1220.6813883094987, (27, 910): 1224.099332907435, (27, 912): 1218.7485300980159, (27, 913): 1212.775259787014, (27, 916): 1210.5616246037443, (27, 926): 1227.0073945665993, (27, 927): 1224.3661298492582, (27, 948): 1220.7675544947608, (27, 961): 1226.2309794675139, (27, 962): 1227.283888813924, (27, 963): 1228.4227261840845, (27, 967): 1237.151551171442, (27, 974): 1232.4012307484877, (27, 998): 1240.1784867119381, (27, 1014): 1418.253288168144, (27, 1086): 1217.2283276820906, (27, 1087): 1217.5292169789714, (27, 1089): 1209.5487700081128, (27, 1090): 1212.7736249990132, (27, 1092): 1224.1700486859852, (27, 1097): 1215.2230527103522, (27, 1107): 1230.6577907738267, (27, 1387): 359.09477554210923, (27, 1554): 367.47182059706995, (27, 1827): 1598.0084530614954, (27, 1828): 1598.86846861099, (27, 1829): 1600.1343612015112, (27, 1830): 1598.8986843650887, (27, 1831): 1599.6219256697825, (27, 1832): 1598.7316161706922, (27, 1833): 1598.8192937262922, (27, 1836): 1597.8611850550058, (27, 1841): 1603.136323249702, (27, 1843): 1600.9327490205465, (27, 1844): 1601.9257327989815, (27, 1845): 1599.3126217218655, (27, 1847): 1590.7876613562917, (27, 1848): 1593.7149092107175, (27, 1849): 1607.4536550146302, (27, 1850): 1608.8794547021596, (27, 1851): 1595.9865427200596, (27, 1852): 1596.2320200132986, (27, 1854): 1597.610332989537, (27, 1856): 1590.4045203585238, (27, 1857): 1593.5286297325483, (27, 1858): 1606.0978982524232, (27, 1861): 1599.9692448587673, (27, 1866): 1590.2425349700547, (27, 1867): 1603.2662293261676, (27, 1868): 1601.478855034535, (27, 1870): 1601.722899362501, (27, 1871): 1602.8471206643487, (27, 1875): 1597.44179500962, (27, 1880): 1592.2148578791812, (27, 1882): 1593.1200028944286, (27, 1883): 1608.9599850472953, (27, 1889): 1593.7065974582658, (27, 1893): 1600.2628695425244, (27, 1894): 1598.1909634370238, (27, 1899): 1591.8701671672181, (27, 1900): 1593.3880583177452, (27, 1902): 1603.8503008111375, (27, 1905): 1606.53009774822, (27, 1907): 1595.6813797962923, (27, 1910): 1596.640554213347, (27, 1917): 1612.0904735128247, (27, 1920): 1595.8634252435493, (27, 1935): 1606.8609512371706, (27, 1937): 1609.1380067407135, (27, 1946): 1587.2469677637137, (27, 1949): 1589.7823874837597, (27, 1950): 1580.8907131249366, (27, 1951): 1585.1874746525666, (27, 1952): 1588.4646754145715, (27, 1953): 1589.8148528851434, (27, 1954): 1587.8205002934317, (27, 1958): 1589.0728546222595, (27, 1960): 1593.4000468508407, (27, 1968): 1595.108456409467, (27, 1969): 1607.3569904798044, (27, 1974): 1604.1547825438788, (27, 1975): 1604.1317774980025, (27, 1979): 1597.9818902799361, (27, 1980): 1597.5348472493151, (27, 1981): 1599.3028890897363, (27, 1985): 1600.7694583736022, (27, 1994): 1577.5473414894564, (27, 2011): 1593.0375764356716, (27, 2019): 1614.6177255421826, (27, 2020): 1611.761518050358, (27, 2029): 1601.0222351368113, (27, 2030): 1609.7807265609154, (27, 2032): 1599.3215287082783, (27, 2033): 1604.9722853034511, (27, 2034): 1604.9272435641255, (27, 2036): 1594.4234946934062, (27, 2037): 1597.0972236933492, (27, 2038): 1597.7587555916532, (27, 2042): 1630.5194058751313, (27, 2050): 1603.4249226455108, (27, 2051): 1603.0052588642084, (27, 2053): 1603.8508412339095, (27, 2054): 1606.7502591085636, (27, 2066): 1600.8594681764748, (27, 2067): 1600.85170467593, (27, 2071): 1572.0714609979466, (27, 2072): 1577.4626952453912, (27, 2073): 1562.5181847323283, (27, 2074): 1561.801047746723, (27, 2080): 1552.7007518882845, (27, 2082): 1580.37858141726, (27, 2083): 1583.1641988906742, (27, 2089): 1577.1926453879746, (27, 2090): 1579.7863472130243, (27, 2092): 1576.2032843597299, (27, 2098): 1556.1601744529355, (27, 2099): 1559.3329274445884, (27, 2101): 1555.6201570859246, (27, 2102): 1570.3538799338776, (27, 2103): 1565.7342766258505, (27, 2104): 1563.2242930534421, (27, 2106): 1585.0731864039976, (27, 2112): 1557.6103775249505, (27, 2113): 1572.4712277069111, (27, 2114): 1576.0850909605383, (27, 2117): 1587.3218214385763, (27, 2123): 1566.183782813629, (27, 2124): 1569.2241698209896, (27, 2134): 1560.413698890713, (27, 2138): 1569.4158668869684, (27, 2141): 1561.5103722508547, (27, 2148): 1565.555343189384, (27, 2150): 1554.0845936478865, (27, 2151): 1557.2458229348758, (27, 2152): 1552.3676869581832, (27, 2153): 1566.6069520838253, (27, 2154): 1554.0301394808894, (27, 2155): 1552.5342275422472, (27, 2156): 1550.2227579151224, (27, 2157): 1553.3017142645408, (27, 2160): 1573.4322098751275, (27, 2161): 1551.7935984206663, (27, 2162): 1567.0520408575405, (27, 2163): 1562.787751031326, (27, 2164): 1562.491806894623, (27, 2168): 1555.0792573199524, (27, 2172): 1557.7767492274618, (27, 2174): 1556.815999283151, (27, 2178): 1560.2415715717034, (27, 2179): 1558.2681760160863, (27, 2183): 1569.1457841010026, (27, 2185): 1569.305812420933, (27, 2186): 1566.8955621983764, (27, 2190): 1574.0745495562167, (27, 2192): 1569.721727293808, (27, 2193): 1570.0162201585172, (27, 2194): 1565.5730720427675, (27, 2195): 1564.8615112588732, (27, 2197): 1570.646637040818, (27, 2205): 1564.3470597448165, (27, 2207): 1556.1717563307498, (27, 2208): 1560.7340727759574, (27, 2212): 1571.4791844186134, (27, 2214): 1480.8025100219807, (27, 2225): 1491.4749233846417, (27, 2231): 1471.7055604264813, (27, 2278): 1536.0356582442657, (27, 2284): 1545.3031447527214, (27, 2285): 1544.0508432234187, (27, 2291): 1526.0516818817337, (27, 2292): 1527.7390563338133, (27, 2307): 1539.3308540555593, (27, 2313): 1524.0137345760588, (27, 2317): 1520.868272006829, (27, 2319): 1530.9268260396275, (27, 2321): 1535.1933117642689, (27, 2323): 1534.5665503071489, (27, 2326): 1550.5452827736096, (27, 2327): 1546.5648443694038, (27, 2329): 1543.8525751657094, (27, 2330): 1540.7736696992476, (27, 2332): 1547.3564368632265, (27, 2344): 1537.1411897973717, (27, 2346): 1536.9824531182207, (27, 2361): 1535.3935839620624, (27, 2368): 1581.7688758234901, (27, 2374): 1586.165345734461, (27, 2375): 1587.6191934782578, (27, 2377): 1572.3166574221934, (27, 2378): 1590.3882081217612, (27, 2379): 1590.8007837684384, (27, 2380): 1592.2916239446556, (27, 2383): 1576.3874026460924, (27, 2385): 1578.744003295083, (27, 2395): 1579.000501111486, (27, 2397): 1588.9955857589737, (27, 2398): 1567.4450123012484, (27, 2399): 1572.9401733481716, (27, 2400): 1571.7066488620867, (27, 2402): 1580.4921700935543, (27, 2403): 1583.9137853245586, (27, 2404): 1584.7844996351007, (27, 2405): 1576.548691120284, (27, 2407): 1583.2441061292936, (27, 2408): 1587.268670023994, (27, 2409): 1579.0431513612489, (27, 2411): 1583.9404730742185, (27, 2412): 1583.021116218574, (27, 2413): 1585.8371504968827, (27, 2414): 1581.2783916435394, (27, 2422): 1582.9190435315725, (27, 2424): 1583.9761561963505, (27, 2426): 1584.7079077215901, (27, 2433): 1578.3472806706573, (27, 2436): 1576.6844401618512, (27, 2437): 1556.6905661039236, (27, 2440): 1561.0879384564275, (27, 2445): 1650.232149138413, (27, 2447): 1639.2309464977945, (27, 2454): 1649.4995680143272, (27, 2455): 1650.0009634640612, (27, 2460): 1618.2101501507861, (27, 2461): 1622.1482171733426, (27, 2471): 1686.2647801412902, (27, 2492): 1624.356706328421, (27, 2511): 1590.9778663611576, (27, 2523): 1608.0501738308792, (27, 2525): 1603.622835516459, (27, 2535): 1608.5910313113038, (27, 2537): 1601.6010610320218, (27, 2538): 1606.3042673004834, (27, 2539): 1604.8618611525844, (27, 2540): 1611.7774245431174, (27, 2542): 1617.0510753505635, (27, 2559): 1716.1778506224778, (27, 2575): 1707.7521801236264, (27, 2599): 1554.8521960724484, (27, 2600): 1588.992694404278, (27, 2607): 1569.0569626646604, (27, 2627): 1614.2338001978953, (27, 2647): 1633.8089686990431, (27, 2674): 1622.9191908160856, (27, 2681): 1620.8944134287558, (27, 2683): 1629.7943027749568, (27, 2686): 1618.9868434010407, (27, 2689): 1741.8424151827835, (27, 2690): 1742.5898540505816, (27, 2713): 1771.4983812599073, (27, 2714): 1774.368437287522, (27, 2715): 1777.3436031754054, (27, 2739): 1774.4641399601333, (27, 2740): 1753.4971632758788, (27, 2741): 1754.8290966397897, (27, 2749): 1771.2223862706528, (27, 2750): 1771.8579567094032, (27, 2752): 1773.8472928666006, (27, 2755): 1776.3872354670805, (27, 2758): 1775.9485271130661, (27, 2759): 1775.8256944554687, (27, 2769): 1772.0308706842152, (27, 2771): 1758.863110372504, (27, 2779): 1761.8660687706868, (27, 2784): 1729.2166951415595, (27, 2800): 1737.4774664023746, (27, 2802): 1748.792565787264, (27, 2803): 1747.4010966922494, (27, 2804): 1745.3050410443232, (27, 2805): 1752.0934101189869, (27, 2807): 1751.6411868485172, (27, 2809): 1751.1259305416568, (27, 2812): 1731.2792553179108, (27, 2814): 1751.950330905797, (27, 2817): 1755.2373259466594, (27, 2819): 1751.389625895063, (27, 2823): 1735.510789337296, (27, 2832): 1756.1850958263885, (27, 2836): 1742.6906012190625, (27, 2839): 1751.3308207162493, (27, 2841): 1754.5483593407357, (27, 2843): 1753.0796408494623, (27, 2846): 1746.4598333463966, (27, 2849): 1758.7483701852566, (27, 2852): 1755.509646402839, (27, 2853): 1760.2562658225224, (27, 2876): 1762.9201851334803, (27, 2877): 1773.9397179544676, (27, 2885): 1780.0138279861415, (27, 2918): 1751.3024161917988, (27, 2921): 1756.2589145728703, (27, 2925): 1732.2624550259516, (27, 2926): 1723.8723923826728, (27, 2930): 1744.1590802086625, (27, 2931): 1734.9235311129032, (27, 2938): 1751.7947187565635, (27, 2940): 1763.3532139616566, (27, 2947): 1746.9178032124885, (27, 2949): 1743.0335466039642, (27, 2950): 1745.5562587207796, (27, 2952): 1743.2655427201453, (27, 2958): 1742.640307665313, (27, 2959): 1744.370895503818, (27, 2960): 1749.6645478635976, (27, 2961): 1747.3951328650346, (27, 2963): 1740.9373107169731, (27, 2968): 1742.6603045480215, (27, 2976): 1740.0643017384532, (27, 2981): 1699.5519219384146, (27, 2982): 1698.8660405667924, (27, 2984): 1696.7285535523574, (27, 3003): 1693.3879802966708, (27, 3046): 1657.497093953109, (27, 3050): 1683.6353424896447, (27, 3051): 1685.2280936308543, (27, 3053): 1680.441241722892, (27, 3069): 1709.3516264913333, (27, 3071): 1678.0276051455394, (27, 3080): 1781.1432906205796, (27, 3199): 1689.7822597003274, (27, 3200): 1684.9593413574405, (27, 3205): 1717.0432256506824, (27, 3209): 1687.7855326642475, (27, 3215): 1684.919706707406, (27, 3217): 1678.5375526402706, (27, 3249): 1685.1190529382075, (27, 3263): 1733.1804153180492, (27, 3289): 1699.3432371019571, (27, 3301): 1701.7995802692817, (27, 3302): 1699.1563947599177, (27, 3307): 1696.1907210046465, (27, 3310): 1704.5494011525193, (27, 3391): 1731.5192381689494, (27, 3509): 647.7354896287646, (27, 3510): 643.1262949758063, (27, 3511): 645.621045781057, (27, 3512): 642.2732619191414, (27, 3514): 642.802699662616, (27, 3519): 661.4934577971562, (27, 3536): 654.8717686356398, (27, 3545): 661.5596919217883, (27, 3548): 653.7799695387895, (27, 3572): 658.1735441126682, (27, 3581): 654.5544548570875, (27, 3583): 649.0041123505123, (27, 3601): 671.1135681365062, (27, 3656): 666.2111834875903, (27, 3669): 663.3712280508449, (27, 3670): 667.7371880316005, (27, 3695): 641.6687551066524, (27, 3696): 644.7936322620294, (27, 3782): 648.0605920249207, (27, 3792): 643.8573037676373, (27, 3989): 1357.2053724339962, (27, 4008): 1382.141684409334, (27, 4031): 1380.3182969845443, (27, 4045): 1371.6603936134738, (27, 4144): 1373.2602947074906, (27, 4145): 1348.6037610690312, (27, 4164): 1363.711175165757, (27, 4168): 1356.101066587022, (27, 4173): 1354.599176056486, (27, 4181): 1339.4346342958147, (27, 4228): 1324.7077013482246, (27, 4248): 1319.0404773013668, (27, 4254): 1186.3174001617788, (27, 4260): 1186.4579556605413, (27, 4262): 1195.3725827337867, (27, 4273): 1193.2593501491924, (27, 4319): 1113.1695050255605, (27, 4326): 1110.3714011619497, (27, 4328): 1111.3294212775327, (27, 4334): 1116.7432730520295, (27, 4335): 1114.8547249977373, (27, 4372): 1125.0038109042764, (27, 4413): 1207.5020179498094, (27, 4434): 1120.7662655560425, (27, 4447): 1128.4768068855185, (27, 4452): 1122.3127900139025, (27, 4463): 981.5557154874673, (27, 4465): 985.529347585299, (27, 4619): 1225.7737237672288, (27, 4645): 1240.7959421955466, (27, 4657): 1239.3357745547792, (27, 4666): 1233.974144419254, (27, 4676): 1245.4308722702865, (27, 4678): 1247.4496733081703, (27, 4689): 1241.0001959578715, (27, 4704): 1298.1458444443767, (27, 4726): 1458.4013350993293, (27, 4727): 1455.5367871947763, (27, 4730): 1449.9172695413547, (27, 4731): 1451.9536888387627, (27, 4734): 1452.6892434218273, (27, 4735): 1450.3346151872045, (27, 4736): 1452.0119689527523, (27, 4737): 1447.6237192757694, (27, 4738): 1448.5184044238376, (27, 4756): 1451.573577860052, (27, 4760): 1435.4859814233853, (27, 4761): 1436.4261388589596, (27, 4762): 1431.990319515707, (27, 4765): 1437.0975597957854, (27, 4773): 1463.688116985809, (27, 4774): 1461.6545932519803, (27, 4790): 1461.7076385244534, (27, 4795): 1459.0772813935027, (27, 4799): 1463.1710973339475, (27, 4801): 1469.8985620946394, (27, 4804): 1459.4075172502164, (27, 4805): 1457.2565973376331, (27, 4806): 1461.3430670038802, (27, 4815): 1459.0634924467329, (27, 4816): 1466.002324969019, (27, 4817): 1468.0391659417278, (27, 4826): 1463.5714102035522, (27, 4830): 1459.7610321785305, (27, 4839): 1443.8400162594287, (27, 4840): 1446.6416187916193, (27, 4841): 1440.8229800555619, (27, 4846): 1438.7426617650367, (27, 4848): 1438.6009641859753, (27, 4850): 1441.2862842179009, (27, 4871): 1405.8942069956129, (27, 4883): 1431.5449996237342, (27, 4900): 1417.6691275479452, (27, 4901): 1414.505858107496, (27, 4917): 1234.5384783456075, (27, 4931): 1214.246706968249, (27, 4944): 1236.442057733588, (27, 4956): 1218.3661612889914, (27, 4958): 1218.5769137539935, (27, 4959): 1215.278984430232, (27, 4961): 1222.1528463664988, (27, 4966): 1213.8678960244956, (27, 5207): 1191.4693945205347, (27, 5272): 785.8519613849687, (27, 5283): 793.2524423931113, (27, 5287): 805.5808661304154, (27, 5289): 808.8735502741849, (27, 5293): 786.9435737141459, (27, 5295): 807.5325001623356, (27, 5296): 807.5824436256033, (27, 5298): 807.470475812249, (27, 5303): 813.8309950784699, (27, 5305): 782.07152343961, (27, 5306): 776.7855125425308, (27, 5307): 778.2544632832288, (27, 5308): 785.5841542799521, (27, 5313): 784.8946026679477, (27, 5314): 789.4591729500386, (27, 5317): 785.8608267887276, (27, 5319): 806.7654150575461, (27, 5324): 802.3665236023404, (27, 5326): 799.5492809673588, (27, 5348): 775.4022332085887, (27, 5351): 781.5734577298872, (27, 5399): 813.676987499971, (27, 5413): 792.4146562014192, (27, 5422): 817.2727609407843, (27, 5445): 800.4637269329949, (27, 5448): 793.396435811654, (27, 5456): 792.1706081848664, (27, 5467): 798.8818768988239, (27, 5624): 720.608865534634, (27, 5671): 946.2997082575575, (27, 5672): 936.7990103125229, (27, 5797): 1060.4544795753102, (27, 5871): 921.5755984092813, (27, 5976): 837.0586620650687, (27, 6118): 1256.7488720002564, (27, 6248): 1378.125078379976, (27, 6345): 477.17475010494536, (27, 6352): 463.7165834973219, (27, 6354): 479.23287635152747, (27, 6359): 484.38714202582815, (27, 6376): 472.1379537055681, (27, 6378): 477.8445977085938, (27, 6381): 484.91102789191626, (27, 6383): 473.2766485351668, (27, 6396): 493.19333565874035, (27, 6399): 480.3028690890428, (27, 6408): 461.6249605729561, (27, 6409): 461.51608786126695, (27, 6419): 429.11264697855546, (27, 6422): 458.1800703539796, (27, 6423): 456.7119073989782, (27, 6424): 470.8864058676955, (27, 6439): 466.15133834361126, (27, 6464): 460.2450629326917, (27, 6465): 460.933299746904, (27, 6469): 467.2579779017926, (27, 6470): 467.4709217483027, (27, 6472): 490.1033983269468, (27, 6480): 477.05775481624045, (27, 6486): 476.3939910593626, (27, 6497): 475.9571842810136, (27, 6503): 449.5275012044445, (27, 6508): 456.7631974699577, (27, 6509): 456.8709255042282, (27, 6521): 474.6340268899361, (27, 6544): 467.83810934670925, (27, 6552): 449.5063140482913, (27, 6553): 446.57869685877176, (27, 6554): 443.69030722074996, (27, 6578): 455.3113377298226, (27, 6582): 446.92140721801354, (27, 6601): 455.28268452277604, (27, 6609): 484.19828954234276, (27, 6610): 483.6681743812976, (27, 6611): 487.63269109706687, (27, 6614): 488.29560137513585, (27, 6615): 487.5776894427747, (27, 6616): 485.9932763476797, (27, 6617): 486.2805023007631, (27, 6618): 485.9700945238829, (27, 6619): 485.620852081317, (27, 6620): 483.981414164991, (27, 6621): 481.2039881387757, (27, 6622): 483.1895938921692, (27, 6623): 485.68359504533134, (27, 6624): 481.3740604505714, (27, 6625): 482.09401745112785, (27, 6626): 486.44931958183156, (27, 6627): 489.65011611945397, (27, 6628): 481.4106146019469, (27, 6629): 479.4261785264208, (27, 6630): 483.6094414938348, (27, 6632): 480.35444697860004, (27, 6634): 479.72202087956754, (27, 6635): 481.47994837579796, (27, 6636): 485.40445923744056, (27, 6637): 475.98142755958423, (27, 6638): 481.8010664141054, (27, 6639): 488.6028637035999, (27, 6640): 483.2936301833732, (27, 6641): 479.5366904823865, (27, 6642): 480.40924003178657, (27, 6643): 487.7623921420449, (27, 6645): 484.95382315754426, (27, 6646): 486.72968713248997, (27, 6647): 481.90573854656185, (27, 6653): 488.14097426683014, (27, 6655): 489.34257670952724, (27, 6658): 478.69186592501455, (27, 6662): 478.7374536355074, (27, 6819): 320.71498915323235, (27, 6996): 334.02019894181154, (27, 7059): 369.43774650442595, (27, 7187): 286.79807207648514, (27, 7304): 213.34924401735944, (27, 7528): 314.10293930863344, (27, 7720): 544.9032481739272, (27, 7793): 537.0546064680301, (27, 7807): 541.074502373103, (27, 7808): 535.3341778626033, (27, 7831): 488.22918336428097, (27, 7850): 529.2272923931952, (27, 7852): 524.5158348336267, (27, 8012): 540.848635201109, (27, 8125): 561.3606353446564, (27, 8208): 613.255704205724, (27, 8392): 490.9110312870478, (27, 8651): 213.90536184039368, (27, 9088): 370.40763571842433, (27, 9443): 24.755786955641817, (27, 9444): 24.3438987066935, (27, 9828): 214.20776212780902, (27, 9868): 192.31710782481483, (27, 10180): 566.0037700225323, (27, 10256): 666.0149937485916, (27, 10276): 618.2998734951503, (27, 10378): 629.5058889258528, (27, 10676): 549.0005031638725, (27, 10714): 492.0389825405931, (27, 10730): 486.27108852205873, (27, 10862): 798.0392809020389, (27, 10881): 810.6262656943154, (27, 10883): 810.5942135370159, (27, 10885): 794.994607305227, (27, 10891): 810.6188606736001, (27, 10909): 806.2432700553935, (27, 10911): 804.6704702710883, (27, 10913): 802.8331135154839, (27, 10915): 800.9780077165577, (27, 10919): 801.2960969301312, (27, 11037): 764.4415644575414, (27, 11039): 718.2352198258965, (27, 11516): 1624.2867593504802, (27, 11856): 1119.1269898770715, (27, 11857): 1115.3265715739226, (27, 11861): 1117.351164165488, (27, 11881): 1113.4574073078734, (27, 11902): 1096.4663853877425, (27, 11911): 1093.662336673834, (27, 11914): 1095.897325706489, (27, 11922): 1108.4301982369832, (27, 11924): 1112.5013211710727, (27, 11926): 1107.623565342791, (27, 11950): 1117.5985912618407, (27, 11963): 1133.5314696373878, (27, 11983): 1123.2107644397809, (27, 11985): 1141.5022903338713, (27, 12009): 1138.7738169016634, (27, 12010): 1127.3719591457368, (27, 12018): 1129.2918918975158, (27, 12020): 1132.2977510242638, (27, 12021): 1134.2159641214794, (27, 12024): 1145.0179209511361, (27, 12025): 1141.2831075880122, (27, 12027): 1138.7451540470327, (27, 12031): 1125.478997286219, (27, 12032): 1129.1720991277884, (27, 12035): 1138.156706856662, (27, 12041): 1142.6855785897671, (27, 12045): 992.8335385460377, (27, 12145): 1062.6013871783996, (27, 12275): 1368.0972500191485, (27, 12294): 1341.4050104511716, (27, 12358): 1431.4887728919482, (27, 12463): 1467.716959269356, (27, 12465): 1466.8234250010826, (27, 12482): 1479.9671893451618, (27, 12503): 1478.3326827828932, (27, 12506): 1482.3591442067661, (27, 12549): 1471.5435221227763, (27, 12559): 1468.8788777955222, (27, 12569): 1472.9232863601171, (27, 12572): 1475.9096876283727, (27, 12574): 1469.4364006862966, (27, 12576): 1474.8031735936024, (27, 12591): 1472.9312270655455, (27, 12608): 1496.6335575981939, (27, 12696): 1456.6309797812455, (27, 12710): 1478.225520608722, (27, 12728): 1468.5028665899783, (27, 12766): 808.8771266615593, (27, 12771): 769.9836283651276, (27, 12790): 766.2448077418208, (27, 12795): 758.7804584353245, (27, 12797): 714.2598112784963, (27, 12798): 719.326580484269, (27, 12811): 751.2302191488329, (27, 12830): 742.128896501133, (27, 12848): 744.5161077738929, (27, 12850): 745.3889266791294, (27, 12852): 739.6466977998987, (27, 12854): 734.7854561681406, (27, 12859): 748.5625196885832, (27, 12861): 723.9975771448841, (27, 12865): 758.6020845737428, (27, 12866): 755.1591708006374, (27, 12867): 765.7413021851809, (27, 12874): 760.7392839770639, (27, 12875): 764.0164540029054, (27, 12881): 750.0256207642083, (27, 12883): 755.9203802509203, (27, 12885): 767.421332087098, (27, 12888): 752.5092201306193, (27, 12889): 750.5369596974931, (27, 12892): 762.1447623185649, (27, 12893): 753.3840844269237, (27, 12896): 755.6141392799734, (27, 12906): 764.0195431767689, (27, 13018): 742.3793141971039, (27, 13071): 748.4065164498141, (27, 13131): 689.9477300876692, (27, 13146): 717.1494842196759, (27, 13159): 702.4854405553367, (27, 13193): 682.4884866456276, (27, 13198): 619.9831621507379, (27, 13292): 680.6709762507152, (27, 13296): 691.6718007487721, (27, 13406): 601.8011957999474, (27, 13407): 601.4440464934187, (27, 13417): 608.9428357759089, (27, 13418): 616.4354923487031, (27, 13438): 630.1847073402341, (27, 13442): 631.1818171481297, (27, 13443): 627.2123503009018, (27, 13764): 484.6262323314095, (27, 13766): 485.97362754637777, (27, 13771): 494.26339118835796, (27, 13783): 467.4650435998779, (27, 13784): 483.41684401161143, (27, 13792): 506.5082926091534, (27, 13824): 468.5073011116146, (27, 14017): 423.0229601861756, (27, 14870): 731.1449711833072, (27, 14997): 259.8337362163669, (27, 15000): 261.9113463683037, (27, 15003): 267.6114812633818, (27, 15006): 270.78543342748617, (27, 15007): 275.08107431536547, (27, 15056): 278.415666188413, (27, 15063): 275.58296508327925, (27, 15069): 276.0280647815385, (27, 15076): 276.561792097488, (27, 15086): 261.994972686528, (27, 15087): 259.07719835199975, (27, 15111): 245.36029206382665, (27, 15116): 253.3435544882131, (27, 15722): 141.72141770414746, (27, 15998): 178.09805480777004, (27, 16073): 998.9743842973292, (27, 16939): 1340.6340619475027, (27, 16940): 1334.5395481645771, (27, 16951): 1341.8925913936255, (27, 16963): 1342.3719046616068, (27, 16965): 1349.6108329640022, (27, 16969): 1348.0792407702625, (27, 16970): 1344.9106255333925, (27, 16971): 1338.3720179860152, (27, 16973): 1338.0904042170046, (27, 16974): 1352.667354762628, (27, 16976): 1345.3239819718153, (27, 16978): 1340.4935682483372, (27, 16980): 1347.6210819601872, (27, 16982): 1352.782172713445, (27, 17045): 1581.6548393080964, (27, 17048): 1590.1465755771153, (27, 17304): 1283.6326087875716, (27, 17305): 1279.4658765586978, (27, 17330): 1283.4594766670796, (27, 17334): 1275.3983434865959, (27, 17343): 1289.6426117825022, (27, 17345): 1275.1476680923674, (27, 17347): 1282.9403025021647, (27, 17351): 1264.2239715309179, (27, 17372): 1274.4954634930773, (27, 17373): 1289.1481070467728, (27, 17377): 1290.1832603348996, (27, 17382): 1280.6518417517862, (27, 17383): 1282.402986434035, (27, 17389): 1276.7827558537474, (27, 17400): 1286.4749233041327, (27, 17401): 1286.2768644828905, (27, 17402): 1287.044008475116, (27, 17403): 1287.9991063496516, (27, 17440): 1275.829294914376, (27, 17455): 1288.0308618660324, (27, 17491): 1289.0246329649408, (27, 17507): 1269.722672000632, (27, 17509): 1275.0370461359532, (27, 17590): 1260.7275211760789, (27, 17615): 1231.7995785606215, (27, 17642): 1236.9958288263158, (27, 17643): 1236.457315116065, (27, 17668): 1231.6440399686353, (27, 17721): 1219.8337349782134, (27, 17754): 1269.9495794736388, (27, 17769): 1271.5917614820205, (27, 17776): 1250.3236290775003, (27, 17804): 1280.2242678514347, (27, 17809): 1285.5453033922104, (27, 17824): 1282.169261498638, (27, 17837): 1266.4360290824013, (27, 17838): 1266.9957368738371, (27, 17862): 1263.0315856296008, (27, 17866): 1274.3663687977216, (27, 17872): 1259.2171175009573, (27, 17873): 1250.5539022024743, (27, 17881): 1263.844667495986, (27, 17947): 852.0106580124377, (27, 17951): 840.2201705422564, (27, 17953): 838.2336862231125, (27, 17954): 839.2379948823852, (27, 17959): 849.1362955995709, (27, 17963): 844.567948200465, (27, 18000): 785.5173723560187, (27, 18001): 788.1416522827774, (27, 18111): 976.8448761814285, (27, 18148): 681.5468165840007, (27, 18166): 800.1393647360472, (27, 18189): 901.7648975336923, (27, 18239): 1291.8341364326188, (27, 18240): 1291.7455640184612, (27, 18245): 1292.3195541339012, (27, 18247): 1291.1262925486956, (27, 18251): 1292.2693213632847, (27, 18256): 1293.4802437766673, (27, 18258): 1292.1282409289433, (27, 18259): 1292.3566250548708, (27, 18260): 1292.8587454821736, (27, 18262): 1293.8308498840433, (27, 18263): 1293.8177746330036, (27, 18264): 1294.3184887460889, (27, 18266): 1294.207579762746, (27, 18267): 1294.7017354090924, (27, 18268): 1294.9366016213735, (27, 18269): 1295.9200971799464, (27, 18275): 1295.4558938164016, (27, 18285): 1294.157466826015, (27, 18308): 1283.8839792273116, (27, 18313): 1280.3319973083633, (27, 18314): 1281.859992185019, (27, 18315): 1295.930339102589, (27, 18316): 1295.81818570825, (27, 18317): 1296.2761647194125, (27, 18320): 1296.7501698253857, (27, 18321): 1296.98840704235, (27, 18322): 1297.7161958768984, (27, 18324): 1298.3510316093343, (27, 18325): 1300.6550012828136, (27, 18326): 1299.7979592938711, (27, 18327): 1296.671977466795, (27, 18329): 1301.7229913713763, (27, 18330): 1300.4811539073394, (27, 18331): 1298.9524355669962, (27, 18332): 1297.3635501098813, (27, 18333): 1300.2657730643693, (27, 18336): 1299.0162604604295, (27, 18337): 1299.8181016272738, (27, 18403): 1298.4935726212084, (27, 18432): 1266.5246958496539, (27, 18451): 1288.146096768646, (27, 18466): 1309.439595870547, (27, 18481): 1296.6096814662392, (27, 18483): 1296.5883479476047, (27, 18484): 1295.3367530264802, (27, 18485): 1291.592430389219, (27, 18486): 1295.0631868429316, (27, 18487): 1292.1437993433208, (27, 18489): 1294.6400962884466, (27, 18490): 1297.6352561765937, (27, 18491): 1299.0219393270959, (27, 18492): 1289.1638338173673, (27, 18493): 1294.595024304081, (27, 18494): 1294.060371216669, (27, 18495): 1296.6050084439862, (27, 18496): 1295.1349848645705, (27, 18497): 1291.4912814177815, (27, 18498): 1292.083460513244, (27, 18499): 1294.235950241187, (27, 18501): 1292.713430494345, (27, 18502): 1291.339049803832, (27, 18503): 1290.25978945235, (27, 18504): 1295.684734923773, (27, 18506): 1292.9778885279247, (27, 18507): 1291.6799257380214, (27, 18508): 1293.9551394993935, (27, 18509): 1294.0014158384045, (27, 18510): 1290.3232516520623, (27, 18511): 1295.0517683434805, (27, 18512): 1293.3875613271896, (27, 18515): 1295.8425466171961, (27, 18516): 1296.0155884567494, (27, 18517): 1294.3095677267625, (27, 18518): 1297.1346650290902, (27, 18519): 1295.971688006049, (27, 18520): 1293.5248992159827, (27, 18522): 1301.7922567858486, (27, 18523): 1302.10978628848, (27, 18532): 1304.0509126289355, (27, 18535): 1300.0363629595588, (27, 18537): 1297.8011733425153, (27, 18539): 1298.2774646712655, (27, 18540): 1298.5471578384472, (27, 18541): 1299.655450730404, (27, 18542): 1300.3575234831064, (27, 18543): 1296.8771138284574, (27, 18546): 1298.5598241408989, (27, 18555): 1302.0661777222374, (27, 18556): 1302.7162203910057, (27, 18565): 1303.8133474491347, (27, 18567): 1304.8708243966455, (27, 18568): 1302.9446431567408, (27, 18577): 1316.652804563911, (27, 18583): 1314.307710450997, (27, 18605): 1317.1395430574714, (27, 18608): 1306.120139699889, (27, 18616): 1329.9353446165528, (27, 18618): 1340.8511347035715, (27, 18625): 1337.0282515912616, (27, 18645): 1327.3730204713174, (27, 18646): 1329.907945745722, (27, 18653): 1320.901426006781, (27, 18654): 1329.6737659051385, (27, 18655): 1323.9288548245654, (27, 18666): 1359.1697253030359, (27, 18837): 1322.3274708664505, (27, 18974): 1288.0405673665987, (27, 18999): 1297.3590794375325, (27, 19000): 1300.6492268400762, (27, 19174): 1149.3031098422507, (27, 19342): 1217.8486407040732, (27, 19455): 1169.519218427673, (27, 19555): 1012.913458426304, (27, 19564): 1028.2156111150916, (27, 19573): 1020.0035375571912, (27, 19586): 1015.964783538022, (27, 19605): 1017.6473644899063, (27, 19611): 1022.9535241050211, (27, 19614): 1019.0053693746058, (27, 19641): 1100.6681033839006, (27, 19702): 1100.9911100898557, (27, 19713): 1094.6518733616306, (27, 19731): 978.7942358548621, (27, 19819): 1147.2674753117212, (27, 19893): 956.5740081693172, (27, 19899): 995.3915068843928, (27, 19929): 966.3297878676884, (27, 19951): 1042.0184530887047, (27, 19962): 973.289792480933, (27, 19970): 988.378765376132, (27, 19971): 989.036741587856, (27, 19972): 982.9197329912984, (27, 19975): 979.6991705957346, (27, 19978): 1056.4778692372488, (27, 19987): 1057.5983032496033, (27, 19989): 1036.847541826229, (27, 20039): 1061.336369738257, (27, 20043): 1069.791704472628, (27, 20047): 1062.987401392662, (27, 20052): 1040.2198924483537, (27, 20054): 1042.1094438722891, (27, 20085): 1144.9075292663422, (27, 20104): 1151.364083990727, (27, 20132): 1111.9703136798748, (27, 20203): 956.5564457489756, (27, 20280): 949.6975294462422, (27, 20285): 948.3156283002558, (27, 20290): 953.0227971194926, (27, 20297): 945.7415693819372, (27, 20309): 1064.4055847576656, (27, 20453): 1170.385365388392, (27, 20485): 900.2518420766014, (27, 20520): 881.8742388439226, (27, 20526): 876.7058784073661, (27, 20698): 644.8395568576535, (27, 20868): 728.07871899707, (27, 21042): 723.5026374903068, (27, 21057): 767.5367584912954, (27, 21066): 745.2627307335096, (27, 21075): 738.0007309141824, (27, 21093): 725.9067729060539, (27, 21098): 756.0013475983288, (27, 21127): 726.6216446052784, (27, 21130): 734.4895285824339, (27, 21144): 734.1030844881498, (27, 21146): 723.7525995257862, (27, 21147): 733.652290549594, (27, 21148): 740.9543992987866, (27, 21153): 727.3718027336033, (27, 21293): 795.1261505176824, (27, 21426): 797.4754513871751, (27, 21442): 847.8549296160409, (27, 21451): 852.6294600654218, (27, 21466): 821.48040397153, (27, 21469): 828.0042902574729, (27, 21471): 818.21554784464, (27, 21473): 823.3764803900362, (27, 21475): 818.504222408247, (27, 21482): 832.883174557358, (27, 21484): 831.1247251143342, (27, 21488): 827.5085278203791, (27, 21494): 817.4189492075278, (27, 21498): 822.5525123617089, (27, 21500): 813.6244764910628, (27, 21514): 823.7948715603956, (27, 21537): 810.0187522435043, (27, 21662): 827.7238515213711, (27, 21691): 800.9992742352275, (27, 21757): 760.7685430105054, (27, 21777): 636.745613770734, (27, 21778): 629.9641852217579, (27, 21779): 633.5746583799926, (27, 21790): 644.6181908960563, (27, 21802): 643.8642419112232, (27, 21824): 650.769300419038, (27, 21874): 635.1712752300377, (27, 21879): 631.0475150272143, (27, 21983): 662.0202544774043, (27, 22002): 733.0864005435585, (27, 22132): 700.6621179677608, (27, 22261): 357.1382783791332, (27, 22298): 355.9975414478015, (27, 22339): 443.56670507830876, (27, 22508): 261.1223829249947, (27, 22841): 1770.393121949864, (27, 22842): 1769.8477862887744, (27, 22874): 1751.732526486315, (27, 22941): 1755.3491089855495, (27, 22956): 1764.7081799594896, (27, 22960): 1769.0029139722853, (27, 22968): 1770.9350022194901, (27, 22970): 1774.7500539528407, (27, 22974): 1774.8254915333334, (27, 22980): 1786.6424126925176, (27, 23025): 1778.747171315271, (27, 23028): 1774.7443010301056, (27, 23081): 1786.7800930402852, (27, 23104): 1755.09727357835, (27, 23147): 1668.0659975297544, (27, 23298): 937.2082705483855, (27, 23376): 917.572718942962, (27, 23381): 903.4940892632592, (27, 23529): 947.7559683512936, (27, 23556): 936.6977763413123, (27, 23718): 927.5222962111154, (27, 24001): 1053.9282265260651, (27, 24094): 1086.3391409855756, (27, 24129): 1105.762968531204, (27, 24174): 1064.3477903813525, (27, 24235): 1106.8503344002152, (27, 24259): 1125.9711721922495, (27, 24260): 1124.485080094418, (27, 24261): 1120.4164553571943, (27, 24305): 1148.3737903854692, (27, 24306): 1151.9845451359445, (27, 24307): 1146.4153512356572, (27, 24308): 1105.4652667517523, (27, 24498): 1199.6807892258014, (27, 24499): 1200.0409625873153, (27, 24500): 1196.5254338731668, (27, 24668): 1176.162111493845, (27, 24711): 1222.6499927153877, (27, 24756): 1234.9863667122984, (27, 24788): 1240.7642723052047, (27, 24809): 1218.7798356035435, (27, 24813): 1225.648895850145, (27, 24821): 1223.3983983030114, (27, 24825): 1225.027962071793, (27, 24832): 1217.320259269048, (27, 24833): 1220.6453632146583, (27, 24835): 1223.9483344448154, (27, 24837): 1229.2642726766976, (27, 24840): 1216.7960976029713, (27, 24841): 1221.9548271834387, (27, 24844): 1216.9358944532194, (27, 24845): 1220.016855456848, (27, 24846): 1219.6585670574475, (27, 24849): 1221.464615367938, (27, 24850): 1226.6448905494192, (27, 24863): 1180.4839093406645, (27, 24866): 1186.4329856959641, (27, 24885): 1193.4387281485467, (27, 24886): 1193.9317831263638, (27, 24889): 1207.0689783913272, (27, 24903): 1212.1870216463826, (27, 24909): 1190.5621955212243, (27, 24999): 1451.0593034673348, (27, 25019): 1444.6733012788002, (27, 25028): 1447.3857849310455, (27, 25137): 975.1070209242041, (27, 25145): 982.1991265178699, (27, 25208): 1076.9037966062044, (27, 25233): 1067.7991954081156, (27, 25371): 967.957308604164, (27, 25377): 945.3036600141488, (27, 25828): 571.3459265969827, (27, 25851): 506.97682100126895, (27, 25874): 562.7464047829857, (27, 25898): 595.0537085668194, (27, 25946): 565.1260902313646, (27, 26047): 698.2769791167393, (27, 26066): 802.4775023277922, (27, 26197): 726.3782600905562, (27, 26212): 450.79397472522476, (27, 26253): 442.6534384747413, (27, 26254): 443.9107402438949, (27, 26257): 452.3280714095808, (27, 26258): 445.85660164537256, (27, 26260): 448.74583600940673, (27, 26266): 432.88021065395316, (27, 26267): 438.3776927946488, (27, 26271): 440.0586968795074, (27, 26304): 470.10461263598364, (27, 26305): 466.3854089274816, (27, 26363): 565.5746456177836, (27, 26441): 522.660237723439, (27, 26442): 519.0569774270944, (27, 26450): 512.2596569372292, (27, 26459): 520.693149020713, (27, 26462): 525.6142731920884, (27, 26467): 547.0416051932998, (27, 26471): 536.4928028063724, (27, 26472): 534.5498843501633, (27, 26473): 533.0474290179408, (27, 26476): 516.713572383583, (27, 26485): 519.8162016465088, (27, 26493): 515.4614742646603, (27, 26524): 532.7807418278079, (27, 26525): 529.4919802490737, (27, 26556): 533.9806409624164, (27, 26560): 540.6561447812521, (27, 26561): 537.8003619346518, (27, 26564): 529.9776663875305, (27, 26569): 534.2207655832046, (27, 26570): 529.5521095800177, (27, 26573): 526.7441730200228, (27, 26581): 523.0705867270763, (27, 26583): 523.6537400246463, (27, 26593): 518.7061621758177, (27, 26837): 545.0496180969164, (27, 26844): 551.7083896504516, (27, 26863): 528.8892315678072, (27, 26893): 544.8296460912896, (27, 26902): 553.7316149865721, (27, 26905): 552.0141275078108, (27, 26912): 556.6024714133457, (27, 26921): 536.990285780389, (27, 26922): 507.6088433626561, (27, 27212): 760.0131131131703, (27, 27218): 761.4200587044277, (27, 27239): 768.6497505576585, (27, 27257): 760.5684616395375, (27, 27274): 769.222531459149, (27, 27279): 765.0795583364805, (27, 27282): 759.1632750788858, (27, 27283): 767.2962748768321, (27, 27285): 770.1359799131171, (27, 27286): 759.4954509880001, (27, 27290): 753.6459314910236, (27, 27295): 754.5403359669006, (27, 27300): 771.4199565564197, (27, 27344): 742.112577284951, (27, 27366): 745.8848333939441, (27, 27383): 764.4469886220846, (27, 27398): 778.9702661943744, (27, 27406): 775.1750984072376, (27, 27407): 779.3085338638797, (27, 27426): 791.7709363940211, (27, 27432): 760.6058162610809, (27, 27460): 782.841618062468, (27, 27523): 701.8842098040432, (27, 27545): 864.7640333168125, (27, 27602): 1000.8510949519356, (27, 27606): 1006.5593805432972, (27, 27646): 799.363847935464, (27, 27667): 828.2469262613331, (27, 27672): 831.6484076112371, (27, 27674): 825.5189019495804, (27, 27688): 837.0854186227693, (27, 27692): 834.5693184523824, (27, 27693): 829.7985639031298, (27, 27705): 827.4485768623722, (27, 27712): 828.0137045368984, (27, 27786): 1079.1313480383847, (27, 27790): 1087.7565479426385, (27, 27791): 1090.0808368718926, (27, 27795): 1068.5860656130073, (27, 27801): 1072.687570223508, (27, 27813): 1080.8959542309694, (27, 27816): 1080.408516371829, (27, 27823): 1073.0831031845808, (27, 27830): 1079.6120129589528, (27, 27884): 729.3444103183364, (27, 27885): 783.9630331993666, (27, 27896): 752.1402651627867, (27, 27919): 752.0964146372326, (27, 27922): 755.6801127888262, (27, 27930): 740.4462785468569, (27, 27934): 740.5921666784928, (27, 27935): 739.9186664657856, (27, 27948): 898.7231610126694, (27, 27951): 934.8675231838777, (27, 28061): 571.6325084170187, (27, 28290): 983.2373827394471, (27, 28292): 987.2665620911671, (27, 28293): 983.6765399165362, (27, 28295): 977.6247141771144, (27, 28296): 981.402827751845, (27, 28297): 980.8622023355126, (27, 28302): 975.5455722578649, (27, 28310): 1087.0433443475454, (27, 28313): 1096.386428119968, (27, 28372): 1091.2931848118662, (27, 28398): 1092.3601138445438, (27, 28399): 1090.1806617420395, (27, 28400): 1094.489484284454, (27, 28401): 1082.4374862592488, (27, 28445): 1094.587149038394, (27, 28475): 1069.8281364323166, (27, 28885): 1100.0416943081939, (27, 28886): 1096.0975117291423, (27, 28915): 1098.155693740988, (27, 28916): 1095.4048786025944, (27, 28917): 1093.1894001780854, (27, 28921): 1107.105349940593, (27, 28931): 1105.8040143766054, (27, 28945): 1084.2678325624722, (27, 28982): 1089.7177244027757, (27, 29219): 1106.4443238134547, (27, 29228): 1090.2517556220566, (27, 29246): 1194.354820278037, (27, 29248): 1192.6829263823183, (27, 29282): 1170.8634329730871, (27, 29290): 1205.349839078376, (27, 29291): 1200.888838221963, (27, 29292): 1205.0212129527406, (27, 29293): 1196.5014207195425, (27, 29294): 1203.1546374423542, (27, 29298): 1197.0646984663051, (27, 29299): 1196.2581519535265, (27, 29304): 1188.4785783619175, (27, 29317): 1168.177422664261, (27, 29323): 1166.6148397350764, (27, 29330): 1176.3708334064465, (27, 29331): 1181.302184376701, (27, 29344): 1107.3920462283081, (27, 29445): 920.4374353221422, (27, 29724): 1764.546505075099, (27, 29738): 1767.6239189784435, (27, 29745): 1759.4993009930934, (27, 29748): 1765.659223405343, (27, 29750): 1772.5576895313568, (27, 29759): 1760.9021602739313, (27, 29772): 1772.33139763898, (27, 29781): 1769.962906779343, (27, 29784): 1766.1162622634236, (27, 29790): 1773.2316911655296, (27, 29811): 1768.7119445646601, (27, 29817): 1801.8303792601225, (27, 29818): 1799.6246944057357, (27, 29929): 1755.7408098161368, (27, 30039): 1784.6443421290046, (27, 30066): 1752.3818686548211, (27, 30116): 1655.679482894598, (27, 30238): 1514.6560639460445, (27, 30248): 1571.0584777490276, (27, 30260): 1571.604465536055, (27, 30545): 1048.0015968653638, (27, 30733): 876.1960872284267, (27, 30756): 824.4370180422466, (27, 30921): 910.6019760872226, (27, 31079): 564.4819119905231, (27, 31149): 519.1866812205403, (27, 31154): 523.3381830757622, (27, 31160): 517.3884462184868, (27, 31163): 520.6283460641727, (27, 31189): 441.1322439035554, (27, 31215): 449.4627876676339, (27, 31259): 459.58617376521624, (27, 31262): 450.0209465462333, (27, 31430): 584.0620690352351, (27, 31568): 434.3232188280561, (27, 31751): 535.2522270822816, (28, 109): 1903.880737753872, (28, 872): 303.4723443815224, (28, 873): 298.6012756133832, (28, 877): 296.46706881826304, (28, 879): 295.3593989235574, (28, 884): 291.6161533617969, (28, 889): 290.30023941050047, (28, 891): 294.35475114210817, (28, 892): 292.45432442150764, (28, 894): 294.6803207212388, (28, 896): 305.8751633572574, (28, 903): 291.7885114955795, (28, 909): 313.1228843848494, (28, 910): 314.7453148410432, (28, 912): 317.2016538033115, (28, 913): 318.6739523548547, (28, 916): 324.55185490584984, (28, 926): 317.92922163597984, (28, 927): 320.38201938718476, (28, 948): 296.8531329496479, (28, 961): 309.5718591025308, (28, 962): 311.554806028087, (28, 963): 312.9738682596853, (28, 967): 291.32330679377344, (28, 974): 284.79568412806515, (28, 998): 286.1599101793166, (28, 1014): 284.63235848770177, (28, 1086): 422.308102389448, (28, 1087): 436.2251597273552, (28, 1089): 433.10379975200084, (28, 1090): 430.2190550467877, (28, 1092): 424.2084310964237, (28, 1097): 426.13488853840903, (28, 1107): 429.8695174206858, (28, 1387): 1505.3307810372344, (28, 1554): 1605.8746459647737, (28, 1827): 274.6680123996503, (28, 1828): 276.09768441451723, (28, 1829): 276.68747738428306, (28, 1830): 272.4818001398985, (28, 1831): 273.6470199838421, (28, 1832): 273.1812413989657, (28, 1833): 273.7929313303933, (28, 1836): 273.59214773125393, (28, 1841): 277.30782734216996, (28, 1843): 275.41633059640805, (28, 1844): 275.74778120499604, (28, 1845): 273.0434819773874, (28, 1847): 267.3898915081329, (28, 1848): 269.65547819395925, (28, 1849): 280.03673051893986, (28, 1850): 281.648312747009, (28, 1851): 269.9950678227959, (28, 1852): 269.00014390161914, (28, 1854): 271.0389991694568, (28, 1856): 265.3849012908319, (28, 1857): 268.8128061261155, (28, 1858): 279.7516444013974, (28, 1861): 275.4579510880543, (28, 1866): 264.1795973220483, (28, 1867): 278.4544231941723, (28, 1868): 277.9710180239423, (28, 1870): 274.05923180884236, (28, 1871): 279.16070281353694, (28, 1875): 271.71968404723566, (28, 1880): 267.9585883790238, (28, 1882): 266.89736146962565, (28, 1883): 283.0467346371775, (28, 1889): 271.3406815748217, (28, 1893): 278.96001165894876, (28, 1894): 277.66710516471693, (28, 1899): 270.77927119394445, (28, 1900): 272.4822894504112, (28, 1902): 281.8957608680731, (28, 1905): 283.25139955441676, (28, 1907): 272.5868387526934, (28, 1910): 275.02498388853473, (28, 1917): 292.1606442132308, (28, 1920): 273.9107675333968, (28, 1935): 286.06683329400124, (28, 1937): 287.49122761700016, (28, 1946): 270.36462520528454, (28, 1949): 273.178633533884, (28, 1950): 262.2041552553317, (28, 1951): 266.68202771516235, (28, 1952): 265.7502016817265, (28, 1953): 270.1914707581107, (28, 1954): 266.08062303494984, (28, 1958): 270.98804224392666, (28, 1960): 273.61438825451063, (28, 1968): 274.6827811539143, (28, 1969): 289.1789728302742, (28, 1974): 285.13806378696034, (28, 1975): 284.2059213436575, (28, 1979): 280.8416575146675, (28, 1980): 277.65675035034604, (28, 1981): 280.9005480374605, (28, 1985): 282.92316049607496, (28, 1994): 253.12475106586214, (28, 2011): 266.02641497282264, (28, 2019): 282.45876617655944, (28, 2020): 280.1885945507955, (28, 2029): 269.88037628213743, (28, 2030): 278.657653904598, (28, 2032): 267.27318127245275, (28, 2033): 273.64612819570914, (28, 2034): 272.66830721716485, (28, 2036): 259.2470180388274, (28, 2037): 262.76455753342645, (28, 2038): 267.7233092209296, (28, 2042): 296.71831507262505, (28, 2050): 273.73151903249595, (28, 2051): 272.2876466618002, (28, 2053): 273.49234145245794, (28, 2054): 275.9861286820655, (28, 2066): 270.7397399462821, (28, 2067): 271.29577645597413, (28, 2071): 249.33848399669245, (28, 2072): 254.83627669535173, (28, 2073): 246.7638288193622, (28, 2074): 245.1545429072501, (28, 2080): 235.37237927229302, (28, 2082): 257.4946667727964, (28, 2083): 260.42314995756516, (28, 2089): 256.4549096062736, (28, 2090): 259.42839445704266, (28, 2092): 257.3074262087006, (28, 2098): 240.22357382329616, (28, 2099): 241.78259770117555, (28, 2101): 238.3469480189687, (28, 2102): 252.097551706783, (28, 2103): 247.20918325657252, (28, 2104): 243.9015805269194, (28, 2106): 261.5081302966332, (28, 2112): 238.8792467339625, (28, 2113): 253.2474703955041, (28, 2114): 254.39383344022656, (28, 2117): 262.61126569340286, (28, 2123): 315.7807147342878, (28, 2124): 318.1252336518936, (28, 2134): 305.2850640216962, (28, 2138): 314.67642779190123, (28, 2141): 307.987843368111, (28, 2148): 288.8879426123109, (28, 2150): 301.16309760825806, (28, 2151): 301.85904814956984, (28, 2152): 298.238390532834, (28, 2153): 291.7775325626202, (28, 2154): 282.9278662215642, (28, 2155): 278.01082514864976, (28, 2156): 278.81339806710173, (28, 2157): 268.13588881955184, (28, 2160): 307.01395570107195, (28, 2161): 295.4571551925177, (28, 2162): 284.23556431828433, (28, 2163): 281.35878928832443, (28, 2164): 279.8577827130282, (28, 2168): 290.0361831052539, (28, 2172): 282.07154789030045, (28, 2174): 298.5938897165175, (28, 2178): 281.23065191617496, (28, 2179): 278.8039930382803, (28, 2183): 311.8052476760176, (28, 2185): 310.5204524315403, (28, 2186): 309.37547833733095, (28, 2190): 309.9409203900649, (28, 2192): 307.29958219027594, (28, 2193): 313.27973006697033, (28, 2194): 310.6881818439917, (28, 2195): 307.1990725418012, (28, 2197): 306.4064907080678, (28, 2205): 298.38211050992373, (28, 2207): 288.89301270383226, (28, 2208): 293.6017288210952, (28, 2212): 320.88477264172985, (28, 2214): 214.08048451998607, (28, 2225): 211.3746962514217, (28, 2231): 277.6905792978658, (28, 2278): 226.1669572797468, (28, 2284): 230.17158568415894, (28, 2285): 227.7756066619054, (28, 2291): 203.96350732088453, (28, 2292): 216.42336294776496, (28, 2307): 224.98141196568085, (28, 2313): 199.15853796345266, (28, 2317): 216.1653792633791, (28, 2319): 217.80982855964214, (28, 2321): 219.4017986150336, (28, 2323): 222.09432812114017, (28, 2326): 241.03877527674214, (28, 2327): 237.87769945310575, (28, 2329): 235.38820800669433, (28, 2330): 231.76446449618837, (28, 2332): 235.46055473787598, (28, 2344): 232.3149532821565, (28, 2346): 229.72791865338317, (28, 2361): 251.095875405564, (28, 2368): 273.57683867822306, (28, 2374): 275.48423074635025, (28, 2375): 277.74469268408535, (28, 2377): 267.1204314009103, (28, 2378): 279.1025726961439, (28, 2379): 277.3634722310399, (28, 2380): 280.0568937163508, (28, 2383): 271.73892080542663, (28, 2385): 274.40317022338945, (28, 2395): 276.7011154430085, (28, 2397): 274.94886776259193, (28, 2398): 263.5950863564639, (28, 2399): 268.92551288524135, (28, 2400): 268.024811553276, (28, 2402): 268.6468726605639, (28, 2403): 271.26955049536826, (28, 2404): 272.79866549590577, (28, 2405): 265.7400907073168, (28, 2407): 272.7445961897921, (28, 2408): 274.92032651026966, (28, 2409): 268.2083373137683, (28, 2411): 267.9011035985674, (28, 2412): 268.43400620508294, (28, 2413): 270.1792536514051, (28, 2414): 266.1519985945924, (28, 2422): 265.95085011486185, (28, 2424): 269.9221791111549, (28, 2426): 271.185908574384, (28, 2433): 264.89018565850887, (28, 2436): 261.3471163281238, (28, 2437): 246.68460777193565, (28, 2440): 250.49360992085616, (28, 2445): 313.5476302042703, (28, 2447): 304.1819875844325, (28, 2454): 313.73450504521713, (28, 2455): 314.9595374625366, (28, 2460): 284.54326524913984, (28, 2461): 288.10278257143625, (28, 2471): 345.67289912321, (28, 2492): 297.2299456160802, (28, 2511): 256.81091733981395, (28, 2523): 277.4718376553222, (28, 2525): 275.2954709453855, (28, 2535): 266.6194239923552, (28, 2537): 259.69318462614643, (28, 2538): 264.19533462505467, (28, 2539): 263.9827579673479, (28, 2540): 269.80075227051765, (28, 2542): 275.37989555877914, (28, 2559): 373.98197196520033, (28, 2575): 365.68802279765345, (28, 2599): 219.4821997380404, (28, 2600): 249.74847113905534, (28, 2607): 235.0677723439848, (28, 2627): 301.71206588838885, (28, 2647): 325.94392092884743, (28, 2674): 307.1956228127392, (28, 2681): 309.11425345603317, (28, 2683): 316.0060510157445, (28, 2686): 303.5944976269631, (28, 2689): 427.8450926577733, (28, 2690): 429.38940448654483, (28, 2713): 485.2374518092944, (28, 2714): 492.22190369707033, (28, 2715): 494.8467340880529, (28, 2739): 491.02942294240427, (28, 2740): 460.6204041851241, (28, 2741): 461.01144973082853, (28, 2749): 492.7945888864339, (28, 2750): 491.7789449931475, (28, 2752): 492.82230169089917, (28, 2755): 496.0474434387937, (28, 2758): 496.9761363576986, (28, 2759): 496.1630609841006, (28, 2769): 491.03295446524174, (28, 2771): 468.4388253410462, (28, 2779): 482.2647205052992, (28, 2784): 458.901654596628, (28, 2800): 478.61755763983916, (28, 2802): 462.18952360911135, (28, 2803): 459.551006200815, (28, 2804): 457.1177193865289, (28, 2805): 469.40290741157264, (28, 2807): 467.5600030816889, (28, 2809): 470.3327536534871, (28, 2812): 448.9714944293281, (28, 2814): 481.02026037867347, (28, 2817): 498.1192645540991, (28, 2819): 463.8691620382923, (28, 2823): 465.91336006012506, (28, 2832): 475.1068098303225, (28, 2836): 462.88886009184733, (28, 2839): 465.8357971748437, (28, 2841): 490.20199299436996, (28, 2843): 486.38266697642405, (28, 2846): 472.33340421122017, (28, 2849): 479.8869264146221, (28, 2852): 476.0191433593861, (28, 2853): 481.7729584644962, (28, 2876): 491.11784714007035, (28, 2877): 502.03564701826383, (28, 2885): 522.1200627718623, (28, 2918): 455.1657265217276, (28, 2921): 461.34890784266275, (28, 2925): 427.6562310450209, (28, 2926): 414.0025843747643, (28, 2930): 453.24646676648763, (28, 2931): 433.578464222315, (28, 2938): 457.90571939912013, (28, 2940): 458.57038719394086, (28, 2947): 440.3330207481053, (28, 2949): 446.93241271102994, (28, 2950): 451.5482578007224, (28, 2952): 449.47473336807377, (28, 2958): 447.95299727384605, (28, 2959): 446.9831041860587, (28, 2960): 452.8168687058001, (28, 2961): 451.70356890834853, (28, 2963): 447.68564618814827, (28, 2968): 450.66452882902695, (28, 2976): 445.48123383689756, (28, 2981): 426.93091076471393, (28, 2982): 429.65702337096405, (28, 2984): 428.5936489790573, (28, 3003): 429.52267572028194, (28, 3046): 361.35519686996025, (28, 3050): 401.1937749499229, (28, 3051): 401.39871906083795, (28, 3053): 398.51364774862157, (28, 3069): 429.18000886704664, (28, 3071): 389.2518914495527, (28, 3080): 528.6067073956901, (28, 3199): 448.6362702972711, (28, 3200): 447.43136902137627, (28, 3205): 470.7676248947798, (28, 3209): 450.0674540395495, (28, 3215): 445.28675348418136, (28, 3217): 440.90480921080587, (28, 3249): 443.1826858868426, (28, 3263): 477.0232673311394, (28, 3289): 447.41045169364827, (28, 3301): 454.4719741179633, (28, 3302): 450.6176116310295, (28, 3307): 447.9304686832357, (28, 3310): 456.44924137455195, (28, 3391): 587.5808267287398, (28, 3509): 719.4012871125228, (28, 3510): 723.89578152521, (28, 3511): 720.1461029828974, (28, 3512): 722.2924883489617, (28, 3514): 720.7811797964509, (28, 3519): 713.0012543920825, (28, 3536): 710.134288657941, (28, 3545): 702.320538026344, (28, 3548): 708.3204553573851, (28, 3572): 708.4995606486077, (28, 3581): 716.6269530050714, (28, 3583): 716.4198499985806, (28, 3601): 706.0998802328537, (28, 3656): 717.0591659155651, (28, 3669): 734.7526171574794, (28, 3670): 731.2993339010053, (28, 3695): 749.5968591988067, (28, 3696): 746.3449067253359, (28, 3782): 698.5129459038942, (28, 3792): 704.3282828612181, (28, 3989): 2684.198876448575, (28, 4008): 2708.193021308839, (28, 4031): 2704.4304175868197, (28, 4045): 2698.017401361857, (28, 4144): 2701.3365018137974, (28, 4145): 2679.336137001281, (28, 4164): 2692.5665566751964, (28, 4168): 2686.063314443525, (28, 4173): 2685.02104950204, (28, 4181): 2670.355486394387, (28, 4228): 2654.274531804002, (28, 4248): 2651.235164812525, (28, 4254): 2526.902592119391, (28, 4260): 2526.689961520192, (28, 4262): 2535.69293914075, (28, 4273): 2533.379403783476, (28, 4319): 2455.3670670873616, (28, 4326): 2452.562289769761, (28, 4328): 2453.4921970389646, (28, 4334): 2458.947779188552, (28, 4335): 2457.078781065194, (28, 4372): 2315.0815404485343, (28, 4413): 2383.5578381706446, (28, 4434): 2313.3344090193154, (28, 4447): 2326.9164524963976, (28, 4452): 2313.724711679868, (28, 4463): 2137.574802741694, (28, 4465): 2144.3284468089496, (28, 4619): 2378.86245375269, (28, 4645): 2398.3951578838696, (28, 4657): 2393.926933256091, (28, 4666): 2385.6092476666227, (28, 4676): 2397.8396527536834, (28, 4678): 2401.3863194192713, (28, 4689): 2390.9966458913377, (28, 4704): 2451.418867209267, (28, 4726): 2558.3693532258512, (28, 4727): 2556.219527374647, (28, 4730): 2552.1899099830252, (28, 4731): 2552.428896732248, (28, 4734): 2560.0178291851034, (28, 4735): 2557.192537094842, (28, 4736): 2557.5360689765594, (28, 4737): 2552.989534312378, (28, 4738): 2552.9186785488464, (28, 4756): 2554.64808802728, (28, 4760): 2547.722733840789, (28, 4761): 2550.490694771704, (28, 4762): 2543.8411310786137, (28, 4765): 2548.317434753911, (28, 4773): 2563.3721260540506, (28, 4774): 2560.110576739689, (28, 4790): 2562.1435561410276, (28, 4795): 2560.6003873253358, (28, 4799): 2560.3298093002973, (28, 4801): 2562.998886345046, (28, 4804): 2563.009306409138, (28, 4805): 2561.721252156997, (28, 4806): 2557.313957629388, (28, 4815): 2554.070472378656, (28, 4816): 2560.0714241333417, (28, 4817): 2559.590237512571, (28, 4826): 2556.855882625969, (28, 4830): 2553.138733963657, (28, 4839): 2553.9107526276043, (28, 4840): 2555.171465829257, (28, 4841): 2550.103698496273, (28, 4846): 2548.8727146563774, (28, 4848): 2547.057563150643, (28, 4850): 2548.7856249541564, (28, 4871): 2529.911553847613, (28, 4883): 2547.2287463013963, (28, 4900): 2540.177761279129, (28, 4901): 2536.44958837152, (28, 4917): 2352.0017824176107, (28, 4931): 2334.7861669239082, (28, 4944): 2354.962816456471, (28, 4956): 2336.934338927351, (28, 4958): 2334.4409760685207, (28, 4959): 2329.8048031639732, (28, 4961): 2341.234878468899, (28, 4966): 2331.5710078867496, (28, 5207): 2312.296904763499, (28, 5272): 2051.645467072402, (28, 5283): 2057.116692062688, (28, 5287): 2061.2095266467045, (28, 5289): 2063.4409091101907, (28, 5293): 2057.2074963149093, (28, 5295): 2073.189305520202, (28, 5296): 2070.242890221481, (28, 5298): 2068.4726462614253, (28, 5303): 2070.775836131763, (28, 5305): 2042.8267951154926, (28, 5306): 2034.3609185990902, (28, 5307): 2039.6344956936346, (28, 5308): 2044.5127956161289, (28, 5313): 2047.8643592458257, (28, 5314): 2052.5259456903204, (28, 5317): 2042.688220336634, (28, 5319): 2064.5791457427163, (28, 5324): 2063.522441742937, (28, 5326): 2063.010170903702, (28, 5348): 2030.5818249170038, (28, 5351): 2030.7870001694246, (28, 5399): 2062.526484189885, (28, 5413): 2031.7323703040163, (28, 5422): 2068.4440170100934, (28, 5445): 2054.071095485399, (28, 5448): 2048.5658632685004, (28, 5456): 2044.2548195474217, (28, 5467): 2048.570482205111, (28, 5624): 1998.0134378835764, (28, 5671): 2214.90644168716, (28, 5672): 2207.656559792735, (28, 5797): 2303.908966142593, (28, 5871): 2114.1250329601216, (28, 5976): 2046.9673324292464, (28, 6118): 512.5334565335028, (28, 6248): 611.0835815386007, (28, 6345): 1773.8214344235366, (28, 6352): 1753.9444596254425, (28, 6354): 1778.2278336231361, (28, 6359): 1782.9820433658915, (28, 6376): 1759.201287789426, (28, 6378): 1775.959573794234, (28, 6381): 1781.9298011133064, (28, 6383): 1769.2675964961925, (28, 6396): 1783.0670605432047, (28, 6399): 1775.0809654193567, (28, 6408): 1753.8119609986243, (28, 6409): 1761.011431094497, (28, 6419): 1725.433531038275, (28, 6422): 1754.697083881877, (28, 6423): 1752.9673043419086, (28, 6424): 1773.8952939690726, (28, 6439): 1769.3927183183425, (28, 6464): 1763.2076166618606, (28, 6465): 1761.9157000789953, (28, 6469): 1765.9343797313686, (28, 6470): 1765.069751146065, (28, 6472): 1790.0530334114044, (28, 6480): 1782.4427582778765, (28, 6486): 1791.0542740015271, (28, 6497): 1787.960787865113, (28, 6503): 1760.7037367009534, (28, 6508): 1764.1401719030434, (28, 6509): 1767.1146213399675, (28, 6521): 1783.4906582999567, (28, 6544): 1780.1802325061403, (28, 6552): 1754.515674550106, (28, 6553): 1751.1808584217893, (28, 6554): 1747.8146346654003, (28, 6578): 1760.3804463797824, (28, 6582): 1755.9068081764892, (28, 6601): 1761.4622631229004, (28, 6609): 1789.9962646593153, (28, 6610): 1790.487377988244, (28, 6611): 1792.278706888075, (28, 6614): 1791.2734688865403, (28, 6615): 1791.4688063262693, (28, 6616): 1793.389756951665, (28, 6617): 1792.4125855390414, (28, 6618): 1795.7596346613018, (28, 6619): 1788.6650278508914, (28, 6620): 1792.7652510454411, (28, 6621): 1789.8408659052473, (28, 6622): 1790.9719918011097, (28, 6623): 1790.1864496584499, (28, 6624): 1786.9628373449486, (28, 6625): 1786.8242220667794, (28, 6626): 1788.8279716185107, (28, 6627): 1791.2302127215748, (28, 6628): 1791.4900455791521, (28, 6629): 1786.8733012014272, (28, 6630): 1785.5909581763435, (28, 6632): 1786.9762905429675, (28, 6634): 1782.1203267440674, (28, 6635): 1789.2143772301788, (28, 6636): 1793.3044449631993, (28, 6637): 1782.9729738942344, (28, 6638): 1785.239586686193, (28, 6639): 1791.0890955967498, (28, 6640): 1786.0735210546318, (28, 6641): 1789.2325989175245, (28, 6642): 1784.8260189294288, (28, 6643): 1789.0359366101397, (28, 6645): 1788.725077022675, (28, 6646): 1795.3004990329835, (28, 6647): 1785.9294373368357, (28, 6653): 1791.5659693264186, (28, 6655): 1791.358962520088, (28, 6658): 1781.630776534577, (28, 6662): 1784.1567819288744, (28, 6819): 1615.64199624367, (28, 6996): 1662.1978510925953, (28, 7059): 1700.3033239409845, (28, 7187): 1626.7799246339926, (28, 7304): 1548.7773276704215, (28, 7528): 1654.0506966581193, (28, 7720): 1884.2910658744358, (28, 7793): 1878.1659630205636, (28, 7807): 1881.7256576458358, (28, 7808): 1876.7373957975794, (28, 7831): 1805.8027038762284, (28, 7850): 1844.7756962393335, (28, 7852): 1837.47912753767, (28, 8012): 1876.0425860158653, (28, 8125): 1900.0466617916113, (28, 8208): 1954.0197343192676, (28, 8392): 1825.2781457912483, (28, 8651): 1433.627022789375, (28, 9088): 1617.6067599338514, (28, 9443): 1324.1152720234254, (28, 9444): 1329.5323369626701, (28, 9828): 1156.6467347677356, (28, 9868): 1150.0875729935012, (28, 10180): 1903.4776705238191, (28, 10256): 2001.4176100580464, (28, 10276): 1956.800136006018, (28, 10378): 1971.6299869391316, (28, 10676): 1869.0379392487546, (28, 10714): 1804.407226997696, (28, 10730): 1816.859076241921, (28, 10862): 1767.482481615507, (28, 10881): 1782.795753166561, (28, 10883): 1780.6434945772892, (28, 10885): 1764.3059513702453, (28, 10891): 1777.31307454151, (28, 10909): 1777.0491548003538, (28, 10911): 1780.3124496843975, (28, 10913): 1776.4179243383085, (28, 10915): 1776.8354585770442, (28, 10919): 1779.4507983350754, (28, 11037): 1663.2961353092285, (28, 11039): 1629.2054867999725, (28, 11516): 2914.679323651565, (28, 11856): 2461.332669605778, (28, 11857): 2457.598574305156, (28, 11861): 2459.5996240153177, (28, 11881): 2455.5681955735718, (28, 11902): 2438.570012374988, (28, 11911): 2435.5824792589688, (28, 11914): 2437.9060833895674, (28, 11922): 2450.5055709353387, (28, 11924): 2454.535396528084, (28, 11926): 2449.6445076830305, (28, 11950): 2459.3911476107082, (28, 11963): 2475.373970516441, (28, 11983): 2464.515625061475, (28, 11985): 2483.3888594094637, (28, 12009): 2480.2465634695313, (28, 12010): 2468.915922859985, (28, 12018): 2470.779812730727, (28, 12020): 2473.86379573923, (28, 12021): 2475.7384331262474, (28, 12024): 2486.57865012994, (28, 12025): 2482.92110641778, (28, 12027): 2480.352844123168, (28, 12031): 2467.0188713257785, (28, 12032): 2470.7955718214744, (28, 12035): 2479.5125821453494, (28, 12041): 2484.74647638116, (28, 12045): 2334.019825340485, (28, 12145): 2403.4614586525677, (28, 12275): 2690.56773634412, (28, 12294): 2660.726231184937, (28, 12358): 2750.1068963974126, (28, 12463): 2784.3139092620113, (28, 12465): 2783.2356099775657, (28, 12482): 2799.076297302928, (28, 12503): 2796.816117275459, (28, 12506): 2800.9924286648356, (28, 12549): 2792.5456149989677, (28, 12559): 2789.2442327481263, (28, 12569): 2792.4579111041635, (28, 12572): 2795.6100078236327, (28, 12574): 2789.088123661209, (28, 12576): 2796.244175050928, (28, 12591): 2795.8164176103905, (28, 12608): 2821.4058232517114, (28, 12696): 2780.9748738601697, (28, 12710): 2805.122381391487, (28, 12728): 2793.1185064466154, (28, 12766): 2109.646443454562, (28, 12771): 2078.9840506096957, (28, 12790): 2074.8112971403416, (28, 12795): 2065.182771206068, (28, 12797): 2025.4390911978464, (28, 12798): 2030.93343722874, (28, 12811): 2062.7613875942916, (28, 12830): 2052.020344236326, (28, 12848): 2057.7265836286383, (28, 12850): 2060.5107382986507, (28, 12852): 2050.550729076669, (28, 12854): 2045.6658777951545, (28, 12859): 2062.6297050995813, (28, 12861): 2036.3753351191988, (28, 12865): 2068.6930073784115, (28, 12866): 2066.221677560706, (28, 12867): 2075.967832744172, (28, 12874): 2071.2343544117048, (28, 12875): 2074.9477325518005, (28, 12881): 2059.7463714253686, (28, 12883): 2065.7917658896663, (28, 12885): 2078.1456476832914, (28, 12888): 2063.0180621693607, (28, 12889): 2061.68061446157, (28, 12892): 2072.2669037013316, (28, 12893): 2063.213011314549, (28, 12896): 2066.1514493024124, (28, 12906): 2071.459151529571, (28, 13018): 2027.9507789767356, (28, 13071): 2028.7264132006494, (28, 13131): 1988.8240265971408, (28, 13146): 2020.8668475498612, (28, 13159): 1977.834235825683, (28, 13193): 1982.5365744699045, (28, 13198): 1925.8829649655102, (28, 13292): 1990.64498957636, (28, 13296): 2009.0592196310686, (28, 13406): 1891.5547348936166, (28, 13407): 1889.8083982059381, (28, 13417): 1886.5003381239706, (28, 13418): 1892.754579592893, (28, 13438): 1916.6469477457795, (28, 13442): 1921.2557702255885, (28, 13443): 1916.5461517998388, (28, 13764): 1529.148970495342, (28, 13766): 1535.021580219171, (28, 13771): 1531.2329768973905, (28, 13783): 1521.0923429738054, (28, 13784): 1540.611422859618, (28, 13792): 1522.9747729941168, (28, 13824): 1517.42432894507, (28, 14017): 1542.4202596684647, (28, 14870): 1791.1350113097542, (28, 14997): 1598.26762348364, (28, 15000): 1599.396197802101, (28, 15003): 1604.0735783912603, (28, 15006): 1611.0711324834722, (28, 15007): 1615.2905150634217, (28, 15056): 1616.2532916196187, (28, 15063): 1612.8406232111663, (28, 15069): 1612.0810368900084, (28, 15076): 1616.2875678255557, (28, 15086): 1602.5933062699924, (28, 15087): 1598.7407526906345, (28, 15111): 1585.7537565673824, (28, 15116): 1593.2538391729524, (28, 15722): 1482.472634206434, (28, 15998): 1424.3267264421374, (28, 16073): 879.8462708348111, (28, 16939): 9.918111234475072, (28, 16940): 14.171556648718823, (28, 16951): 3.162227694530833, (28, 16963): 0.2379716217390773, (28, 16965): 7.846903364676216, (28, 16969): 7.351654492149161, (28, 16970): 4.24160188905958, (28, 16971): 4.051872536636842, (28, 16973): 5.544034462505631, (28, 16974): 10.392489062851872, (28, 16976): 7.07098242901053, (28, 16978): 6.573039759417231, (28, 16980): 12.309605380057825, (28, 16982): 11.675602922920616, (28, 17045): 403.3859137815815, (28, 17048): 408.5437610820118, (28, 17304): 2618.6545628001554, (28, 17305): 2613.580899632961, (28, 17330): 2617.8454389918165, (28, 17334): 2610.6369398634406, (28, 17343): 2623.794860847659, (28, 17345): 2609.417653800369, (28, 17347): 2616.671953958044, (28, 17351): 2599.5375250009047, (28, 17372): 2609.379943006144, (28, 17373): 2623.456122046504, (28, 17377): 2624.3683961766556, (28, 17382): 2615.0080027278755, (28, 17383): 2617.0574831873823, (28, 17389): 2611.457338732413, (28, 17400): 2621.1386765722827, (28, 17401): 2621.0976343583866, (28, 17402): 2621.603654460794, (28, 17403): 2622.4623184541124, (28, 17440): 2608.971377202227, (28, 17455): 2621.5396106897624, (28, 17491): 2621.732103366469, (28, 17507): 2607.0587356393667, (28, 17509): 2612.527707306833, (28, 17590): 2594.995973899647, (28, 17615): 2571.4675612338438, (28, 17642): 2576.3211611902984, (28, 17643): 2575.540273681456, (28, 17668): 2571.454215257092, (28, 17721): 2560.800912308995, (28, 17754): 2610.946471655351, (28, 17769): 2609.782113537902, (28, 17776): 2587.261151524213, (28, 17804): 2618.4813452533394, (28, 17809): 2623.767373318921, (28, 17824): 2620.858460911994, (28, 17837): 2602.950669362818, (28, 17838): 2603.011916518073, (28, 17862): 2598.836311097491, (28, 17866): 2610.323796944659, (28, 17872): 2595.3585393641115, (28, 17873): 2586.4663444780713, (28, 17881): 2600.0328029750945, (28, 17947): 565.5411228804621, (28, 17951): 572.161369930534, (28, 17953): 575.5197671685312, (28, 17954): 576.4198565746877, (28, 17959): 563.2570852669166, (28, 17963): 562.0840348949553, (28, 18000): 604.8558867502438, (28, 18001): 605.6015758823773, (28, 18111): 641.5359138362354, (28, 18148): 802.0435167689975, (28, 18166): 743.9895742621088, (28, 18189): 670.3658877525838, (28, 18239): 2626.490573549115, (28, 18240): 2626.2927749011055, (28, 18245): 2626.914849737534, (28, 18247): 2625.6146058297336, (28, 18251): 2626.730578528635, (28, 18256): 2627.782426628959, (28, 18258): 2626.3778748542736, (28, 18259): 2626.5435637377254, (28, 18260): 2626.955958288068, (28, 18262): 2627.840161641606, (28, 18263): 2628.0530050852526, (28, 18264): 2628.471958958318, (28, 18266): 2628.111739245613, (28, 18267): 2628.5405847437364, (28, 18268): 2628.7002658754764, (28, 18269): 2629.5400321026677, (28, 18275): 2629.1432510145514, (28, 18285): 2628.383123462842, (28, 18308): 2619.50993635971, (28, 18313): 2616.121290244831, (28, 18314): 2617.2525940800683, (28, 18315): 2629.8758176949545, (28, 18316): 2629.618264083452, (28, 18317): 2629.9995539182705, (28, 18320): 2630.624537143132, (28, 18321): 2630.7513240278463, (28, 18322): 2631.389474004157, (28, 18324): 2632.1716273019138, (28, 18325): 2634.4119087381964, (28, 18326): 2633.5856996998987, (28, 18327): 2630.194637090325, (28, 18329): 2635.6229081911, (28, 18330): 2633.9312887662395, (28, 18331): 2632.522630449152, (28, 18332): 2630.976574773868, (28, 18333): 2633.8615019570857, (28, 18336): 2632.8788204073057, (28, 18337): 2633.756822061524, (28, 18403): 2631.587305122628, (28, 18432): 2595.5220132658105, (28, 18451): 2619.9671820708104, (28, 18466): 2644.1220554837496, (28, 18481): 2630.9391830293416, (28, 18483): 2630.811933374009, (28, 18484): 2629.6757524122972, (28, 18485): 2626.379365233367, (28, 18486): 2630.1258809200035, (28, 18487): 2627.404327619349, (28, 18489): 2629.364950371945, (28, 18490): 2632.5620880586894, (28, 18491): 2633.912892758002, (28, 18492): 2624.415800778991, (28, 18493): 2629.790844821697, (28, 18494): 2628.716087765068, (28, 18495): 2631.5738390786223, (28, 18496): 2630.0575642789386, (28, 18497): 2626.8891901987745, (28, 18498): 2627.0541196659206, (28, 18499): 2629.112094740887, (28, 18501): 2627.837685685968, (28, 18502): 2626.53452096522, (28, 18503): 2625.3870170528103, (28, 18504): 2630.465647379525, (28, 18506): 2628.381407580273, (28, 18507): 2627.2063176298816, (28, 18508): 2628.9437066941764, (28, 18509): 2629.0852424072937, (28, 18510): 2625.589714870168, (28, 18511): 2630.4340504370075, (28, 18512): 2628.6488475442043, (28, 18515): 2630.7637981171365, (28, 18516): 2631.2653780897244, (28, 18517): 2629.7905617678166, (28, 18518): 2632.2479778518405, (28, 18519): 2630.680046223627, (28, 18520): 2628.408745226438, (28, 18522): 2636.046753084079, (28, 18523): 2636.4694113426967, (28, 18532): 2638.503004911592, (28, 18535): 2634.4146542309927, (28, 18537): 2632.138283941201, (28, 18539): 2632.6834686606435, (28, 18540): 2633.02142306546, (28, 18541): 2634.202049813928, (28, 18542): 2634.9390299737784, (28, 18543): 2631.331517553052, (28, 18546): 2633.2680254164825, (28, 18555): 2636.847860635814, (28, 18556): 2637.587713959374, (28, 18565): 2638.4146192651556, (28, 18567): 2639.7153028645093, (28, 18568): 2637.6546742086466, (28, 18577): 2651.5998194709423, (28, 18583): 2648.9053343781557, (28, 18605): 2651.4089368052687, (28, 18608): 2641.4272124636036, (28, 18616): 2664.4556800825962, (28, 18618): 2675.777920478831, (28, 18625): 2671.048141855045, (28, 18645): 2660.846961821652, (28, 18646): 2663.7196603467532, (28, 18653): 2655.354947710864, (28, 18654): 2664.3245457672942, (28, 18655): 2658.6206965180695, (28, 18666): 2693.1179090250935, (28, 18837): 2638.297462288143, (28, 18974): 2616.622452232368, (28, 18999): 2624.2783942598403, (28, 19000): 2627.6059490997654, (28, 19174): 2461.464763365227, (28, 19342): 2526.797663631152, (28, 19455): 2491.7738049820227, (28, 19555): 2325.4718735990755, (28, 19564): 2334.142811103, (28, 19573): 2327.2899791636555, (28, 19586): 2324.305624788064, (28, 19605): 2327.144694768448, (28, 19611): 2331.819876883713, (28, 19614): 2330.004751575159, (28, 19641): 2409.545411043509, (28, 19702): 2407.787783235905, (28, 19713): 2402.043376863103, (28, 19731): 2299.9420341661107, (28, 19819): 2465.7415629199877, (28, 19893): 2282.1601652783816, (28, 19899): 2316.051815557374, (28, 19929): 2291.8674622103003, (28, 19951): 2362.2691068260106, (28, 19962): 2296.077243196637, (28, 19970): 2314.6886844766054, (28, 19971): 2314.2900886370844, (28, 19972): 2307.8217429357687, (28, 19975): 2305.533765596745, (28, 19978): 2380.63944188274, (28, 19987): 2382.3758866358107, (28, 19989): 2362.903199462509, (28, 20039): 2386.2128151950897, (28, 20043): 2395.08132190655, (28, 20047): 2389.4883143537527, (28, 20052): 2367.3458000389537, (28, 20054): 2368.701242722048, (28, 20085): 2471.4905135895156, (28, 20104): 2477.7839016601424, (28, 20132): 2438.512143919149, (28, 20203): 2271.34707460734, (28, 20280): 2260.9856045320334, (28, 20285): 2257.955386406024, (28, 20290): 2264.8747626717104, (28, 20297): 2258.4128828384037, (28, 20309): 2380.0649227303597, (28, 20453): 2487.59515433655, (28, 20485): 2217.5284303699273, (28, 20520): 2201.2649202418625, (28, 20526): 2192.4679267821807, (28, 20698): 1409.8084676678525, (28, 20868): 1228.4160006232685, (28, 21042): 2063.313325412599, (28, 21057): 2106.890727381158, (28, 21066): 2085.4416370346203, (28, 21075): 2077.378443865644, (28, 21093): 2066.47476286294, (28, 21098): 2097.246561566227, (28, 21127): 2066.8353235524332, (28, 21130): 2074.9994213430846, (28, 21144): 2073.876376843803, (28, 21146): 2063.9884459683785, (28, 21147): 2073.183641834601, (28, 21148): 2080.7050276018304, (28, 21153): 2063.194723179905, (28, 21293): 2135.3229442360976, (28, 21426): 2125.5299857487603, (28, 21442): 2172.062555223965, (28, 21451): 2176.542065356356, (28, 21466): 2148.604678328526, (28, 21469): 2155.436781554861, (28, 21471): 2145.14254376755, (28, 21473): 2150.7753935607957, (28, 21475): 2145.7200999407646, (28, 21482): 2159.7993313395978, (28, 21484): 2158.3521783607766, (28, 21488): 2154.359384642977, (28, 21494): 2145.611681240785, (28, 21498): 2150.720816434448, (28, 21500): 2142.582968145362, (28, 21514): 2156.130066563408, (28, 21537): 2140.9775959916583, (28, 21662): 2162.1097205565634, (28, 21691): 2135.2211437587175, (28, 21757): 2087.840200997094, (28, 21777): 1978.8541756938964, (28, 21778): 1972.0742463570573, (28, 21779): 1975.7798343308145, (28, 21790): 1986.578181774337, (28, 21802): 1986.0573547662532, (28, 21824): 1993.0237044252829, (28, 21874): 1977.4409702403427, (28, 21879): 1973.3041704819175, (28, 21983): 2002.7546779791564, (28, 22002): 2075.243921861281, (28, 22132): 2031.4670286513788, (28, 22261): 1148.3371538935273, (28, 22298): 1166.5131292275018, (28, 22339): 1112.5740648207884, (28, 22508): 1269.1538451436375, (28, 22841): 897.3264542570757, (28, 22842): 894.3261471459699, (28, 22874): 875.8538757264533, (28, 22941): 886.9890930747076, (28, 22956): 889.3082975316486, (28, 22960): 898.0220104951653, (28, 22968): 861.8693751600624, (28, 22970): 869.191653326066, (28, 22974): 846.0190869324889, (28, 22980): 852.1276652842173, (28, 23025): 814.8021883748926, (28, 23028): 805.8333456069346, (28, 23081): 771.9484552681511, (28, 23104): 698.7423760539857, (28, 23147): 750.8283810296897, (28, 23298): 2273.6167558729862, (28, 23376): 2254.1685973332987, (28, 23381): 2242.4559628359752, (28, 23529): 2285.972347850924, (28, 23556): 2274.7354936103557, (28, 23718): 2261.732458260994, (28, 24001): 2388.68628494283, (28, 24094): 2424.7662521822767, (28, 24129): 2444.045825227305, (28, 24174): 2404.118671917594, (28, 24235): 2447.0372426996914, (28, 24259): 2465.354119666717, (28, 24260): 2463.989110114944, (28, 24261): 2459.8405832991275, (28, 24305): 2487.2925367266735, (28, 24306): 2491.0388069896185, (28, 24307): 2485.413534686119, (28, 24308): 2436.376263916554, (28, 24498): 2535.4161456974266, (28, 24499): 2535.850918545968, (28, 24500): 2532.2782846667683, (28, 24668): 2507.3311199889404, (28, 24711): 2559.8998068328824, (28, 24756): 2573.361769239698, (28, 24788): 2578.6222611779876, (28, 24809): 2557.8629095544316, (28, 24813): 2564.2768906410984, (28, 24821): 2562.1373967495692, (28, 24825): 2563.8646263880078, (28, 24832): 2556.3429361151702, (28, 24833): 2559.5925268653095, (28, 24835): 2562.872945944293, (28, 24837): 2567.939340055487, (28, 24840): 2555.8932890158626, (28, 24841): 2560.8032537999634, (28, 24844): 2556.113969052558, (28, 24845): 2558.7891525015384, (28, 24846): 2558.9088302301047, (28, 24849): 2560.7149480248127, (28, 24850): 2565.358578861566, (28, 24863): 2519.631405459663, (28, 24866): 2525.4134446903204, (28, 24885): 2532.545406299516, (28, 24886): 2533.2092092494313, (28, 24889): 2545.344328317397, (28, 24903): 2549.998533800673, (28, 24909): 2528.4235210675943, (28, 24999): 2776.0233278797564, (28, 25019): 2768.4613382744483, (28, 25028): 2772.8361786252817, (28, 25137): 2265.685408122287, (28, 25145): 2273.2919781100127, (28, 25208): 2353.300976525915, (28, 25233): 2342.773706595355, (28, 25371): 2271.032118759119, (28, 25377): 2250.8940713699835, (28, 25828): 1868.0988378902055, (28, 25851): 1812.2121091307868, (28, 25874): 1866.7411481210402, (28, 25898): 1889.5887024668682, (28, 25946): 1862.2848017583192, (28, 26047): 1980.1590266578198, (28, 26066): 2127.132850475128, (28, 26197): 2033.8515794817379, (28, 26212): 1676.3687208631952, (28, 26253): 1657.3904583143726, (28, 26254): 1664.3817813724636, (28, 26257): 1671.7846593677098, (28, 26258): 1661.4259663749438, (28, 26260): 1666.6939247526607, (28, 26266): 1657.7008433392546, (28, 26267): 1664.215040282363, (28, 26271): 1664.6429269637574, (28, 26304): 1731.2654409480765, (28, 26305): 1730.2041867375765, (28, 26363): 1846.9632380149067, (28, 26441): 1248.7009925696134, (28, 26442): 1247.9328824130223, (28, 26450): 1256.4623078130116, (28, 26459): 1267.1337213059528, (28, 26462): 1270.4280812982065, (28, 26467): 1247.69270229716, (28, 26471): 1248.8344363894469, (28, 26472): 1247.998126939546, (28, 26473): 1246.8007518654197, (28, 26476): 1235.6139267631982, (28, 26485): 1258.2005564554347, (28, 26493): 1252.7943145986735, (28, 26524): 1271.5392295344216, (28, 26525): 1269.6458213758622, (28, 26556): 1252.415545942922, (28, 26560): 1261.7314741279013, (28, 26561): 1268.6196337784047, (28, 26564): 1252.204342394494, (28, 26569): 1266.9922453477416, (28, 26570): 1265.7075633432128, (28, 26573): 1259.9149313665075, (28, 26581): 1256.0785792199893, (28, 26583): 1260.2885479178824, (28, 26593): 1250.9610881798942, (28, 26837): 1241.9720147312419, (28, 26844): 1238.7467454011362, (28, 26863): 1235.908356673527, (28, 26893): 1222.234245193464, (28, 26902): 1217.447022047401, (28, 26905): 1231.3058253659954, (28, 26912): 1224.7411962415695, (28, 26921): 1229.9486630640872, (28, 26922): 1226.0676672335078, (28, 27212): 1443.0696491118822, (28, 27218): 1456.422856552796, (28, 27239): 1435.9037998805675, (28, 27257): 1434.8832595778026, (28, 27274): 1432.8501616810522, (28, 27279): 1429.4013025112463, (28, 27282): 1432.5916632442809, (28, 27283): 1439.0484809609784, (28, 27285): 1429.0375912178122, (28, 27286): 1424.9917860544347, (28, 27290): 1434.6994033529318, (28, 27295): 1442.5804196068746, (28, 27300): 1433.8853554099974, (28, 27344): 1424.63826413691, (28, 27366): 1417.0463202900714, (28, 27383): 1420.3942151071924, (28, 27398): 1426.3463053202215, (28, 27406): 1432.3466601494645, (28, 27407): 1434.6457818758975, (28, 27426): 1465.8004310415292, (28, 27432): 1470.8349992455426, (28, 27460): 1471.228155661637, (28, 27523): 1354.9081800539605, (28, 27545): 1372.3077928968994, (28, 27602): 1289.047873870527, (28, 27606): 1293.7606369637792, (28, 27646): 1275.7605662103724, (28, 27667): 1258.1322291076506, (28, 27672): 1260.4193503741856, (28, 27674): 1261.3824477972094, (28, 27688): 1271.5094427982922, (28, 27692): 1253.7901795740934, (28, 27693): 1255.698538442641, (28, 27705): 1252.2063725142248, (28, 27712): 1248.1930964729747, (28, 27786): 1425.9228943634282, (28, 27790): 1477.7484875074865, (28, 27791): 1484.9520727755148, (28, 27795): 1424.0018880607474, (28, 27801): 1458.311422931674, (28, 27813): 1419.2592821285955, (28, 27816): 1430.1970467042545, (28, 27823): 1460.0335104106223, (28, 27830): 1442.8665161576537, (28, 27884): 1271.800733447005, (28, 27885): 1277.8658133693082, (28, 27896): 1275.6724947478099, (28, 27919): 1278.8401288604994, (28, 27922): 1274.6424207986404, (28, 27930): 1276.7643656941675, (28, 27934): 1274.0160466890286, (28, 27935): 1270.7911605663892, (28, 27948): 1119.7520006916407, (28, 27951): 1173.0157305381306, (28, 28061): 878.9961687125135, (28, 28290): 696.0246398807191, (28, 28292): 678.0404212466088, (28, 28293): 691.300989758018, (28, 28295): 682.7841936794885, (28, 28296): 690.9699426100245, (28, 28297): 704.5016774135032, (28, 28302): 696.7179502745776, (28, 28310): 434.6261954735197, (28, 28313): 448.4080992890775, (28, 28372): 414.3538811832386, (28, 28398): 416.3923610698868, (28, 28399): 420.15342404436853, (28, 28400): 418.35110718149696, (28, 28401): 419.1174376584803, (28, 28445): 460.97232261001926, (28, 28475): 401.47746349842697, (28, 28885): 2442.296075145378, (28, 28886): 2438.367346319809, (28, 28915): 2440.424182899835, (28, 28916): 2437.683486022839, (28, 28917): 2435.4611770287565, (28, 28921): 2449.3388979846427, (28, 28931): 2448.059511869473, (28, 28945): 2426.1880764939733, (28, 28982): 2431.8763356301847, (28, 29219): 2446.4403457433086, (28, 29228): 2430.364225017166, (28, 29246): 2531.3788251705905, (28, 29248): 2528.667621960158, (28, 29282): 2507.4296790962367, (28, 29290): 2543.2161468858694, (28, 29291): 2538.5573493782067, (28, 29292): 2542.742580305763, (28, 29293): 2534.3732689087137, (28, 29294): 2540.504739034196, (28, 29298): 2534.679377417551, (28, 29299): 2533.6295626681986, (28, 29304): 2526.544587021742, (28, 29317): 2506.8874410539024, (28, 29323): 2505.3978334001577, (28, 29330): 2514.8122609941092, (28, 29331): 2519.7630185243643, (28, 29344): 2445.791675537214, (28, 29445): 2256.00232974297, (28, 29724): 1006.1802924249481, (28, 29738): 1007.325957967779, (28, 29745): 1008.6297064919837, (28, 29748): 1032.7255831827074, (28, 29750): 1044.436710933437, (28, 29759): 1028.3147227586312, (28, 29772): 1032.8613560861268, (28, 29781): 1032.5327242415071, (28, 29784): 1021.6987138049268, (28, 29790): 1037.6540093478318, (28, 29811): 1045.4535137444732, (28, 29817): 1114.8604961612132, (28, 29818): 1114.9322520788592, (28, 29929): 993.6132041521216, (28, 30039): 944.6583211868867, (28, 30066): 896.8083184161785, (28, 30116): 910.8409304002112, (28, 30238): 949.1599490337996, (28, 30248): 858.9216418348808, (28, 30260): 852.4787814953036, (28, 30545): 2389.4241741308074, (28, 30733): 2215.749617855011, (28, 30756): 2166.598319923193, (28, 30921): 2252.278038399412, (28, 31079): 1808.4162298650506, (28, 31149): 1786.9430216250796, (28, 31154): 1787.05277453815, (28, 31160): 1785.6402523043364, (28, 31163): 1784.2939773765868, (28, 31189): 1712.4579631468903, (28, 31215): 1716.3182040722124, (28, 31259): 1705.6128042171, (28, 31262): 1697.9398924954146, (28, 31430): 1814.8954507468884, (28, 31568): 1608.7705180883445, (28, 31751): 1768.3064296412792, (29, 109): 372.8081875813155, (29, 872): 1772.793172954143, (29, 873): 1781.1109129026004, (29, 877): 1778.2868406862033, (29, 879): 1779.5498186696086, (29, 884): 1771.861298212576, (29, 889): 1776.9326989640715, (29, 891): 1769.0275373829813, (29, 892): 1785.9367547830318, (29, 894): 1784.7648259564937, (29, 896): 1776.2611283492256, (29, 903): 1778.9400393402198, (29, 909): 1763.8074601665064, (29, 910): 1766.8679278509953, (29, 912): 1761.4310106970772, (29, 913): 1755.5392745660727, (29, 916): 1752.6534535967994, (29, 926): 1769.2435103275432, (29, 927): 1766.3920678668903, (29, 948): 1765.9634194323544, (29, 961): 1769.574278078166, (29, 962): 1770.3297078594005, (29, 963): 1771.2400864972483, (29, 967): 1782.3358465194228, (29, 974): 1778.5746650932704, (29, 998): 1785.8745788107192, (29, 1014): 1964.0392998450154, (29, 1086): 1745.0021543068203, (29, 1087): 1743.1154470464394, (29, 1089): 1735.899936463296, (29, 1090): 1739.4659854458807, (29, 1092): 1751.4259387120999, (29, 1097): 1742.4703944788453, (29, 1107): 1756.8469402250955, (29, 1387): 503.75766032767694, (29, 1554): 376.2511246916467, (29, 1827): 2159.223380520441, (29, 1828): 2159.9694712878104, (29, 1829): 2161.3424669664805, (29, 1830): 2160.6772920655635, (29, 1831): 2161.3078489362083, (29, 1832): 2160.34714124955, (29, 1833): 2160.3353000679513, (29, 1836): 2159.2478929381773, (29, 1841): 2164.7545294548568, (29, 1843): 2162.516568843695, (29, 1844): 2163.6246237800733, (29, 1845): 2161.0582663274245, (29, 1847): 2152.1028386254593, (29, 1848): 2155.113418913709, (29, 1849): 2169.3350081598487, (29, 1850): 2170.7086612943285, (29, 1851): 2157.7168636975866, (29, 1852): 2158.1972824557665, (29, 1854): 2159.432938200409, (29, 1856): 2152.0185544125447, (29, 1857): 2155.049564722787, (29, 1858): 2167.78299935484, (29, 1861): 2161.3756087437814, (29, 1866): 2152.051940591847, (29, 1867): 2164.689931127485, (29, 1868): 2162.6816352383134, (29, 1870): 2163.7139305384626, (29, 1871): 2164.0660917485925, (29, 1875): 2159.1045636199756, (29, 1880): 2153.6674830911165, (29, 1882): 2154.926611989617, (29, 1883): 2170.529163291747, (29, 1889): 2154.8007483716183, (29, 1893): 2161.0832900399164, (29, 1894): 2158.9016646051605, (29, 1899): 2152.7644638194483, (29, 1900): 2154.229837989426, (29, 1902): 2164.7408688288865, (29, 1905): 2167.6288925849663, (29, 1907): 2156.8807878238363, (29, 1910): 2157.56375037041, (29, 1917): 2172.5101590870977, (29, 1920): 2156.8564190566212, (29, 1935): 2167.504242291737, (29, 1937): 2169.905346690748, (29, 1946): 2147.497103091388, (29, 1949): 2149.9486108325877, (29, 1950): 2141.5314708555807, (29, 1951): 2145.735851645101, (29, 1952): 2149.687848577333, (29, 1953): 2150.4851169461804, (29, 1954): 2148.881447384092, (29, 1958): 2149.4947944648975, (29, 1960): 2154.0481875350392, (29, 1968): 2155.8436404825725, (29, 1969): 2167.5332237096436, (29, 1974): 2164.5213384936264, (29, 1975): 2164.6575816168397, (29, 1979): 2158.1154870649266, (29, 1980): 2158.142045203517, (29, 1981): 2159.6314828576587, (29, 1985): 2160.9822080258323, (29, 1994): 2139.210032750505, (29, 2011): 2154.9952202642603, (29, 2019): 2177.4416156572975, (29, 2020): 2174.476956905895, (29, 2029): 2163.738482377533, (29, 2030): 2172.4138072404958, (29, 2032): 2162.251410558326, (29, 2033): 2167.6930289970546, (29, 2034): 2167.8559963721073, (29, 2036): 2158.126559668335, (29, 2037): 2160.5730170345505, (29, 2038): 2160.27096319836, (29, 2042): 2193.6121673587945, (29, 2050): 2165.8110786839484, (29, 2051): 2165.611966040779, (29, 2053): 2166.3729930527165, (29, 2054): 2169.332491721715, (29, 2066): 2163.359524373648, (29, 2067): 2163.2343873222644, (29, 2071): 2133.511525444624, (29, 2072): 2138.8134408866226, (29, 2073): 2122.9748611907667, (29, 2074): 2122.4064529339103, (29, 2080): 2113.55503698327, (29, 2082): 2141.735757101748, (29, 2083): 2144.4603993331484, (29, 2089): 2138.2266647383326, (29, 2090): 2140.7206328594834, (29, 2092): 2136.9467171465953, (29, 2098): 2116.7477965620815, (29, 2099): 2120.1168707362885, (29, 2101): 2116.4197546955456, (29, 2102): 2131.080420516718, (29, 2103): 2126.5730673411763, (29, 2104): 2124.227431519432, (29, 2106): 2146.489923805939, (29, 2112): 2118.604423428477, (29, 2113): 2133.3225797163473, (29, 2114): 2137.294763883944, (29, 2117): 2148.916351537696, (29, 2123): 2117.6596174087795, (29, 2124): 2120.6843131134783, (29, 2134): 2112.705327642712, (29, 2138): 2121.348386672287, (29, 2141): 2113.5561488443, (29, 2148): 2120.498359605153, (29, 2150): 2106.3136542973944, (29, 2151): 2109.6800170167903, (29, 2152): 2104.8111850500304, (29, 2153): 2121.2764655852498, (29, 2154): 2108.5863408925325, (29, 2155): 2107.5748758527943, (29, 2156): 2104.9345524693135, (29, 2157): 2109.698435467496, (29, 2160): 2126.78081406653, (29, 2161): 2104.5376897077344, (29, 2162): 2122.7732271201517, (29, 2163): 2118.4383926358596, (29, 2164): 2118.310269495214, (29, 2168): 2108.824896913684, (29, 2172): 2112.816549126316, (29, 2174): 2109.629077789319, (29, 2178): 2115.6432919496892, (29, 2179): 2113.7844402686596, (29, 2183): 2121.4297916653536, (29, 2185): 2121.774760852868, (29, 2186): 2119.27838568271, (29, 2190): 2127.0986386690247, (29, 2192): 2122.6567395492793, (29, 2193): 2122.1915341004, (29, 2194): 2117.655867417726, (29, 2195): 2117.3311055096106, (29, 2197): 2123.7926241766004, (29, 2205): 2117.9180814576957, (29, 2207): 2110.169959183046, (29, 2208): 2114.570398214858, (29, 2212): 2122.793884090789, (29, 2214): 2037.2812643264328, (29, 2225): 2049.047472873688, (29, 2231): 2020.6804510704442, (29, 2278): 2096.1076532296984, (29, 2284): 2105.9516141858276, (29, 2285): 2104.88800644397, (29, 2291): 2088.0334816506966, (29, 2292): 2088.1670340546375, (29, 2307): 2099.9691212084294, (29, 2313): 2086.4461385440163, (29, 2317): 2080.5671691100056, (29, 2319): 2091.5418640658486, (29, 2321): 2096.109274569676, (29, 2323): 2095.025547306978, (29, 2326): 2110.2907381920895, (29, 2327): 2106.2706262554334, (29, 2329): 2103.5797906056987, (29, 2330): 2100.635981098748, (29, 2332): 2107.501195643599, (29, 2344): 2096.508839974711, (29, 2346): 2096.6798416848414, (29, 2361): 2092.1638144886824, (29, 2368): 2140.744326274927, (29, 2374): 2145.4445582354474, (29, 2375): 2146.7480806674844, (29, 2377): 2131.0253096943884, (29, 2378): 2149.689951800153, (29, 2379): 2150.437360209413, (29, 2380): 2151.7118246028035, (29, 2383): 2134.9366051256534, (29, 2385): 2137.201993075523, (29, 2395): 2137.1544343374694, (29, 2397): 2148.7588454120228, (29, 2398): 2126.055678329326, (29, 2399): 2131.464814332982, (29, 2400): 2130.207705592664, (29, 2402): 2140.048879703853, (29, 2403): 2143.5374466520693, (29, 2404): 2144.2905128282628, (29, 2405): 2136.014268699719, (29, 2407): 2142.545725114572, (29, 2408): 2146.790064594198, (29, 2409): 2138.4692629461265, (29, 2411): 2144.10378638803, (29, 2412): 2142.9661329369683, (29, 2413): 2145.90950382324, (29, 2414): 2141.3369234821494, (29, 2422): 2143.2484574967852, (29, 2424): 2143.8211581677087, (29, 2426): 2144.456766557867, (29, 2433): 2138.1902194375866, (29, 2436): 2136.8492506827192, (29, 2437): 2116.3931891327734, (29, 2440): 2120.7960473277917, (29, 2445): 2213.9899569166814, (29, 2447): 2202.5881669742357, (29, 2454): 2212.9899239542647, (29, 2455): 2213.284174994093, (29, 2460): 2181.3625267519647, (29, 2461): 2185.364669331236, (29, 2471): 2251.3637563036164, (29, 2492): 2194.558738945774, (29, 2511): 2160.335667212148, (29, 2523): 2177.877328368711, (29, 2525): 2173.650547814964, (29, 2535): 2175.9875691009056, (29, 2537): 2169.0506018831725, (29, 2538): 2173.558993408387, (29, 2539): 2172.8596800325013, (29, 2540): 2179.1696578266024, (29, 2542): 2184.672718017371, (29, 2559): 2282.5480998061025, (29, 2575): 2275.0474564614415, (29, 2599): 2118.8973840966273, (29, 2600): 2153.900108403063, (29, 2607): 2132.675332432722, (29, 2627): 2185.292193141213, (29, 2647): 2205.1171210255397, (29, 2674): 2193.8569966141226, (29, 2681): 2192.007582760231, (29, 2683): 2200.8477955451835, (29, 2686): 2189.927660571846, (29, 2689): 2313.1806023781583, (29, 2690): 2313.963271386986, (29, 2713): 2343.442760984915, (29, 2714): 2346.318585597688, (29, 2715): 2349.293793058777, (29, 2739): 2346.4143080059407, (29, 2740): 2325.3844110813657, (29, 2741): 2326.70680862917, (29, 2749): 2343.1658843296095, (29, 2750): 2343.805709119521, (29, 2752): 2345.796369196799, (29, 2755): 2348.3346353347574, (29, 2758): 2347.8923154924373, (29, 2759): 2347.7715683757374, (29, 2769): 2343.98014385878, (29, 2771): 2330.7779168110515, (29, 2779): 2333.814717232696, (29, 2784): 2301.1442836920305, (29, 2800): 2309.2869133237105, (29, 2802): 2320.7269285501743, (29, 2803): 2319.3274289397664, (29, 2804): 2317.2278542841227, (29, 2805): 2324.042139427823, (29, 2807): 2323.586740320564, (29, 2809): 2323.0762472015613, (29, 2812): 2303.2241671554107, (29, 2814): 2323.8650685952553, (29, 2817): 2326.987730029559, (29, 2819): 2323.3201942601454, (29, 2823): 2307.429456067303, (29, 2832): 2328.135427161163, (29, 2836): 2314.6409315541287, (29, 2839): 2323.2714141079264, (29, 2841): 2326.3987701408773, (29, 2843): 2324.95715568836, (29, 2846): 2318.3965761956447, (29, 2849): 2330.696241759031, (29, 2852): 2327.4590341660714, (29, 2853): 2332.202989467481, (29, 2876): 2334.832445255456, (29, 2877): 2345.8435097136357, (29, 2885): 2351.725215474722, (29, 2918): 2323.1457220913917, (29, 2921): 2328.124436212256, (29, 2925): 2303.9044790875487, (29, 2926): 2295.334724827324, (29, 2930): 2316.05854388496, (29, 2931): 2306.649433079643, (29, 2938): 2323.6686813004403, (29, 2940): 2335.04197666965, (29, 2947): 2318.5305549414807, (29, 2949): 2314.867869359319, (29, 2950): 2317.422527509593, (29, 2952): 2315.1322095669957, (29, 2958): 2314.4945404381606, (29, 2959): 2316.1864289172045, (29, 2960): 2321.4952058769168, (29, 2961): 2319.2405431464904, (29, 2963): 2312.808297729214, (29, 2968): 2314.5474046534514, (29, 2976): 2311.9171214760154, (29, 2981): 2271.500535578624, (29, 2982): 2270.8061043973144, (29, 2984): 2268.6655789240262, (29, 3003): 2265.3051803366507, (29, 3046): 2229.194256189613, (29, 3050): 2255.5543140153854, (29, 3051): 2257.1383857981887, (29, 3053): 2252.3611334675034, (29, 3069): 2281.2959254793486, (29, 3071): 2249.880628784175, (29, 3080): 2352.7494712726448, (29, 3199): 2261.4329100453588, (29, 3200): 2256.5609869121545, (29, 3205): 2288.70384874871, (29, 3209): 2259.3811175928654, (29, 3215): 2256.5591985008505, (29, 3217): 2250.162570328996, (29, 3249): 2256.797021188039, (29, 3263): 2304.9608446218276, (29, 3289): 2271.134384465577, (29, 3301): 2273.518519152251, (29, 3302): 2270.9003709247063, (29, 3307): 2267.9377357661947, (29, 3310): 2276.2734539129747, (29, 3391): 2299.190239101565, (29, 3509): 1219.335108767713, (29, 3510): 1214.7138354898675, (29, 3511): 1217.2926021832304, (29, 3512): 1213.9982090337435, (29, 3514): 1214.5775246308658, (29, 3519): 1232.6427903069473, (29, 3536): 1226.6137877396902, (29, 3545): 1233.3701843751628, (29, 3548): 1225.6402195597623, (29, 3572): 1229.8404318424602, (29, 3581): 1225.9152073028806, (29, 3583): 1220.7061195518986, (29, 3601): 1242.1094510243058, (29, 3656): 1236.605132022706, (29, 3669): 1232.0273587806146, (29, 3670): 1236.354365421699, (29, 3695): 1210.838423116276, (29, 3696): 1214.0271761196063, (29, 3782): 1219.2337054005595, (29, 3792): 1215.326225750646, (29, 3989): 847.1170931849688, (29, 4008): 873.0579211428584, (29, 4031): 875.4257552792772, (29, 4045): 862.3566444480846, (29, 4144): 860.0946280844184, (29, 4145): 830.2217285466227, (29, 4164): 849.1571521355775, (29, 4168): 839.2709177365507, (29, 4173): 836.7368359534382, (29, 4181): 820.9410007528096, (29, 4228): 810.066640362876, (29, 4248): 798.1351806840119, (29, 4254): 641.8667638816073, (29, 4260): 643.7240557227411, (29, 4262): 651.9929894176631, (29, 4273): 650.8693035169806, (29, 4319): 557.9790168099981, (29, 4326): 555.350848733113, (29, 4328): 556.7761718761235, (29, 4334): 561.3618911068113, (29, 4335): 559.0928240921725, (29, 4372): 701.2006796707461, (29, 4413): 784.7437669708102, (29, 4434): 694.965945381495, (29, 4447): 694.8171577695542, (29, 4452): 697.5173840878214, (29, 4463): 630.8646216402472, (29, 4465): 630.3405210186016, (29, 4619): 823.172238009295, (29, 4645): 831.2969917991315, (29, 4657): 833.0294785474576, (29, 4666): 831.4495118546303, (29, 4676): 840.2862531896607, (29, 4678): 840.489937400935, (29, 4689): 838.9319653724241, (29, 4704): 884.2085005390883, (29, 4726): 1070.1191014921267, (29, 4727): 1067.0232542376352, (29, 4730): 1060.791776772372, (29, 4731): 1064.0753733995903, (29, 4734): 1058.9562153329516, (29, 4735): 1057.2957925052517, (29, 4736): 1059.8834791602899, (29, 4737): 1056.1882248096547, (29, 4738): 1057.7820357856633, (29, 4756): 1061.5610984025861, (29, 4760): 1039.780833660886, (29, 4761): 1039.0442437075778, (29, 4762): 1037.0626935704593, (29, 4765): 1042.0517806652044, (29, 4773): 1074.9695355824242, (29, 4774): 1074.2192725796783, (29, 4790): 1072.6129631348847, (29, 4795): 1069.4080559074407, (29, 4799): 1076.6232314604845, (29, 4801): 1085.8603936501877, (29, 4804): 1067.956467511553, (29, 4805): 1065.3539046542749, (29, 4806): 1076.0196916735622, (29, 4815): 1074.8384690237542, (29, 4816): 1081.66093530733, (29, 4817): 1085.5239131024648, (29, 4826): 1080.195714211158, (29, 4830): 1076.802857238829, (29, 4839): 1048.9106016475662, (29, 4840): 1052.6603419893572, (29, 4841): 1046.9474585291211, (29, 4846): 1044.4125864145128, (29, 4848): 1045.7097136930465, (29, 4850): 1048.8610013570044, (29, 4871): 1003.8498162814259, (29, 4883): 1033.4009486537834, (29, 4900): 1015.423026944021, (29, 4901): 1013.1526258150076, (29, 4917): 865.1029934634768, (29, 4931): 845.6778967619762, (29, 4944): 865.6419777694841, (29, 4956): 850.9186636605721, (29, 4958): 853.7023862466368, (29, 4959): 852.3371639222138, (29, 4961): 853.4864515780431, (29, 4966): 848.1256135693718, (29, 5207): 827.1022962058221, (29, 5272): 340.24166506842505, (29, 5283): 348.5665304572692, (29, 5287): 371.2642868019379, (29, 5289): 375.2455706183683, (29, 5293): 332.58636276011305, (29, 5295): 354.77666636569415, (29, 5296): 360.16602490568346, (29, 5298): 363.0367332061876, (29, 5303): 374.36597232230315, (29, 5305): 347.17983603586606, (29, 5306): 349.7956912123558, (29, 5307): 343.6696861438874, (29, 5308): 352.70213513460413, (29, 5313): 344.86400644568147, (29, 5314): 347.5846258595229, (29, 5317): 356.6839678089977, (29, 5319): 368.2007663365748, (29, 5324): 359.3988148233593, (29, 5326): 353.4086541658043, (29, 5348): 353.35268549685, (29, 5351): 367.73127439656264, (29, 5399): 388.1629131043005, (29, 5413): 391.2714217661681, (29, 5422): 386.54698636421324, (29, 5445): 371.5332067492642, (29, 5448): 364.3317766582071, (29, 5456): 369.0376658803224, (29, 5467): 377.3776724402026, (29, 5624): 278.1655265376511, (29, 5671): 455.9636065846943, (29, 5672): 444.8101529431298, (29, 5797): 585.3087147379825, (29, 5871): 543.6380016209831, (29, 5976): 464.6131476281461, (29, 6118): 1817.1079225578328, (29, 6248): 1931.2526423170043, (29, 6345): 352.8461428699702, (29, 6352): 371.06731397109377, (29, 6354): 346.2240276135111, (29, 6359): 346.7437877736369, (29, 6376): 377.7683645227067, (29, 6378): 348.80218523816967, (29, 6381): 350.99725374334884, (29, 6383): 355.07436627851905, (29, 6396): 369.0554899619208, (29, 6399): 357.4520316065436, (29, 6408): 366.48961997873215, (29, 6409): 347.44784074343266, (29, 6419): 362.52006447479187, (29, 6422): 355.9494587857331, (29, 6423): 356.8847704149811, (29, 6424): 336.1152255978657, (29, 6439): 336.23039485134075, (29, 6464): 338.0830268996522, (29, 6465): 343.4819715006257, (29, 6469): 348.7348606213295, (29, 6470): 351.60217760488865, (29, 6472): 342.40217699351, (29, 6480): 328.23942857818224, (29, 6486): 298.82422736352726, (29, 6497): 307.79279727608986, (29, 6503): 316.1395799265158, (29, 6508): 325.9953950047966, (29, 6509): 317.2685291647566, (29, 6521): 318.0620146182481, (29, 6544): 308.23831008081225, (29, 6552): 334.49149077910363, (29, 6553): 336.31780259187855, (29, 6554): 338.34038809783806, (29, 6578): 333.0571382641527, (29, 6582): 323.481465670933, (29, 6601): 329.84279043348454, (29, 6609): 326.0152577510618, (29, 6610): 322.98375853512016, (29, 6611): 329.0526742990854, (29, 6614): 333.9000015233608, (29, 6615): 331.29810331110093, (29, 6616): 320.9045980614351, (29, 6617): 324.7419505401375, (29, 6618): 313.3819784495562, (29, 6619): 334.00382860690735, (29, 6620): 316.8490040932415, (29, 6621): 317.7092775266705, (29, 6622): 320.0850259564515, (29, 6623): 329.70663976611576, (29, 6624): 327.01775787349925, (29, 6625): 329.48174816206466, (29, 6626): 335.84182429692186, (29, 6627): 337.80777286381203, (29, 6628): 313.11604681585055, (29, 6629): 321.6588542215292, (29, 6630): 337.3095247686351, (29, 6632): 324.0429452414572, (29, 6634): 336.59500646019086, (29, 6635): 320.4744137645464, (29, 6636): 319.42026760518456, (29, 6637): 323.5760421106548, (29, 6638): 333.31790716092496, (29, 6639): 335.298355405545, (29, 6640): 335.04625654227283, (29, 6641): 314.6274266617726, (29, 6642): 330.63247949430087, (29, 6643): 338.8768081920092, (29, 6645): 331.95478293299794, (29, 6646): 317.1476028827956, (29, 6647): 331.59180898592416, (29, 6653): 332.6078487453698, (29, 6655): 336.5821727277139, (29, 6658): 335.17523579490233, (29, 6662): 327.89256450863763, (29, 6819): 405.6445771110992, (29, 6996): 315.4824415947086, (29, 7059): 283.25792317569653, (29, 7187): 285.22278764655215, (29, 7304): 387.9831259104546, (29, 7528): 285.35831767269457, (29, 7720): 155.7835049991794, (29, 7793): 132.91421154003905, (29, 7807): 139.77146330213503, (29, 7808): 127.75146164395785, (29, 7831): 286.41287879090123, (29, 7850): 290.19211826758675, (29, 7852): 299.5794527135333, (29, 8012): 193.3413984969684, (29, 8125): 15.817666557237471, (29, 8208): 146.86389004167694, (29, 8392): 207.74466826032864, (29, 8651): 565.5557669591935, (29, 9088): 474.71783610177664, (29, 9443): 587.7395863193868, (29, 9444): 581.9455929618504, (29, 9828): 754.9262503019193, (29, 9868): 761.719311488811, (29, 10180): 5.948533020333525, (29, 10256): 94.8542684241551, (29, 10276): 48.148822144167006, (29, 10378): 95.75158230510344, (29, 10676): 104.06204765418124, (29, 10714): 155.18433419727342, (29, 10730): 100.58237186937005, (29, 10862): 730.247272308663, (29, 10881): 733.0650075012802, (29, 10883): 735.0784972786082, (29, 10885): 729.0884515721444, (29, 10891): 738.2845672047033, (29, 10909): 732.4599622383244, (29, 10911): 727.1361770205385, (29, 10913): 728.3240925094909, (29, 10915): 725.3403246635582, (29, 10919): 723.2567704455893, (29, 11037): 780.9241415191393, (29, 11039): 753.9940783130554, (29, 11516): 1163.729127218727, (29, 11856): 563.685054336345, (29, 11857): 558.0375539710343, (29, 11861): 560.9310669747136, (29, 11881): 559.639401512994, (29, 11902): 543.0583062801455, (29, 11911): 542.4499896601396, (29, 11914): 543.6839346360961, (29, 11922): 555.1710374762692, (29, 11924): 559.6689356694251, (29, 11926): 555.0369519894333, (29, 11950): 567.0707400573568, (29, 11963): 582.2349459062197, (29, 11983): 576.2059149314844, (29, 11985): 589.6504119639075, (29, 12009): 590.2600552979967, (29, 12010): 578.6074839512686, (29, 12018): 580.8877337490763, (29, 12020): 583.2598120912501, (29, 12021): 585.4524793128878, (29, 12024): 595.7411270750565, (29, 12025): 591.5114143235479, (29, 12027): 589.2564698747024, (29, 12031): 576.7878902969948, (29, 12032): 579.7720359351483, (29, 12035): 590.4520065544131, (29, 12041): 589.0003623335666, (29, 12045): 450.92445697711383, (29, 12145): 520.2227232500695, (29, 12275): 867.1831392237287, (29, 12294): 848.3097507228761, (29, 12358): 935.1613191651238, (29, 12463): 973.4569434878695, (29, 12465): 972.9395658688105, (29, 12482): 980.5690580140359, (29, 12503): 980.15715448482, (29, 12506): 983.7367682652095, (29, 12549): 968.949277568779, (29, 12559): 967.5987346655966, (29, 12569): 973.0317529078566, (29, 12572): 975.5839321301675, (29, 12574): 969.473446033381, (29, 12576): 971.2435913221022, (29, 12591): 966.6698565514371, (29, 12608): 985.8264385877142, (29, 12696): 948.119585623411, (29, 12710): 963.7802642608668, (29, 12728): 959.0066563089384, (29, 12766): 442.1796108972584, (29, 12771): 394.359784766364, (29, 12790): 393.4324431267483, (29, 12795): 395.56536921070216, (29, 12797): 356.1667558184262, (29, 12798): 357.3685686285272, (29, 12811): 375.2696873800116, (29, 12830): 375.30792570796694, (29, 12848): 365.886714023344, (29, 12850): 359.9481931950697, (29, 12852): 370.6750665437797, (29, 12854): 368.05187880365355, (29, 12859): 365.3767660281099, (29, 12861): 357.268623665759, (29, 12865): 384.17142891650127, (29, 12866): 379.07070422323017, (29, 12867): 388.008410553256, (29, 12874): 384.1696126405687, (29, 12875): 384.75780375086384, (29, 12881): 380.334654741004, (29, 12883): 383.28240509767903, (29, 12885): 387.4678325704126, (29, 12888): 379.28190558998585, (29, 12889): 376.1120857506101, (29, 12892): 386.1771057213051, (29, 12893): 381.9360844833762, (29, 12896): 381.0059557813725, (29, 12906): 395.5243784990731, (29, 13018): 442.76804804590205, (29, 13071): 458.45748442082254, (29, 13131): 382.55343260047414, (29, 13146): 381.07913615500945, (29, 13159): 448.19439222939855, (29, 13193): 375.9629719368402, (29, 13198): 336.030019839045, (29, 13292): 344.26485205822684, (29, 13296): 323.1335374997588, (29, 13406): 378.5998568229635, (29, 13407): 382.19098107994057, (29, 13417): 410.95470206666, (29, 13418): 415.78517807671767, (29, 13438): 394.5953041300891, (29, 13442): 385.4235511152356, (29, 13443): 386.2331718169783, (29, 13764): 717.1158973661848, (29, 13766): 713.0961812888225, (29, 13771): 725.6762041588291, (29, 13783): 706.1664990976468, (29, 13784): 704.9853204960531, (29, 13792): 746.4162660758153, (29, 13824): 710.7035178602152, (29, 14017): 636.7294936877862, (29, 14870): 610.4991995356942, (29, 14997): 312.37261826144004, (29, 15000): 310.74227472635783, (29, 15003): 305.6804098264017, (29, 15006): 301.2897368507308, (29, 15007): 296.97963638855435, (29, 15056): 293.99157870560134, (29, 15063): 297.1519704776681, (29, 15069): 297.5391223046645, (29, 15076): 295.3977979628281, (29, 15086): 310.19022452037444, (29, 15087): 312.8731361269764, (29, 15111): 326.6775665878675, (29, 15116): 318.6148818672573, (29, 15722): 430.2289332459874, (29, 15998): 497.55718922661936, (29, 16073): 1512.5273095468024, (29, 16939): 1907.2520794966847, (29, 16940): 1901.0596684760742, (29, 16951): 1909.1313431032497, (29, 16963): 1909.4729448161688, (29, 16965): 1916.559910605243, (29, 16969): 1915.3751042962197, (29, 16970): 1911.8395098519675, (29, 16971): 1905.4163798608938, (29, 16973): 1905.3564475076, (29, 16974): 1919.7627327575772, (29, 16976): 1912.1043109032164, (29, 16978): 1907.2819029746279, (29, 16980): 1914.1665442635817, (29, 16982): 1920.099633100525, (29, 17045): 2152.4974491289568, (29, 17048): 2161.00392722893, (29, 17304): 756.3399273021738, (29, 17305): 754.8990650696625, (29, 17330): 757.9862683353895, (29, 17334): 747.7599718246192, (29, 17343): 764.6014129279239, (29, 17345): 750.3046392316566, (29, 17347): 759.3089524490839, (29, 17351): 736.7563578209276, (29, 17372): 747.9199025990625, (29, 17373): 763.6902483024425, (29, 17377): 765.0312206554895, (29, 17382): 755.3640001789322, (29, 17383): 756.2067731084123, (29, 17389): 750.7295050552295, (29, 17400): 760.1089768712123, (29, 17401): 759.4705489625055, (29, 17402): 760.9530729666989, (29, 17403): 762.146539134488, (29, 17440): 754.085097124015, (29, 17455): 764.8194409649612, (29, 17491): 767.9299374277667, (29, 17507): 735.7884158541464, (29, 17509): 740.4395183448036, (29, 17590): 736.4321231364618, (29, 17615): 690.397966960725, (29, 17642): 696.8528237160647, (29, 17643): 697.27845155983, (29, 17668): 689.6497204755007, (29, 17721): 672.6558990309486, (29, 17754): 721.6716886454512, (29, 17769): 734.7281194004676, (29, 17776): 718.2920541838984, (29, 17804): 742.898570283279, (29, 17809): 748.2008280635055, (29, 17824): 743.272558451519, (29, 17837): 735.2333700644398, (29, 17838): 737.3169853089502, (29, 17862): 734.1312900989828, (29, 17866): 744.621545981614, (29, 17872): 729.4149006596872, (29, 17873): 721.7580533587452, (29, 17881): 733.7427418152574, (29, 17947): 1393.4674130083831, (29, 17951): 1382.609159118892, (29, 17953): 1380.1506921377006, (29, 17954): 1380.660200231088, (29, 17959): 1391.8946724380237, (29, 17963): 1388.7490514360466, (29, 18000): 1332.5535784450499, (29, 18001): 1334.1764885495188, (29, 18111): 1478.6989745618175, (29, 18148): 1190.4055023056692, (29, 18166): 1300.668491762873, (29, 18189): 1406.060274213485, (29, 18239): 765.3024277255097, (29, 18240): 765.5250641608327, (29, 18245): 765.9436408408905, (29, 18247): 765.093099374656, (29, 18251): 766.2721014425248, (29, 18256): 767.8852643343026, (29, 18258): 766.7274103162767, (29, 18259): 767.1220282547099, (29, 18260): 767.855015683979, (29, 18262): 769.0351447881671, (29, 18263): 768.3971955188919, (29, 18264): 769.1070176560296, (29, 18266): 769.6876835314495, (29, 18267): 770.3431378935436, (29, 18268): 770.7751695452591, (29, 18269): 772.1144307193877, (29, 18275): 771.4837411301851, (29, 18285): 768.7514810444408, (29, 18308): 754.8176850898402, (29, 18313): 750.8967347432623, (29, 18314): 753.5489866403218, (29, 18315): 771.235089489938, (29, 18316): 771.525338485235, (29, 18317): 772.1760490695258, (29, 18320): 772.2205465502166, (29, 18321): 772.7547658605474, (29, 18322): 773.7002761811063, (29, 18324): 773.9110004823073, (29, 18325): 776.3059550875338, (29, 18326): 775.3956812814287, (29, 18327): 773.102589387449, (29, 18329): 776.9463552034973, (29, 18330): 776.9683244498115, (29, 18331): 775.1712007020883, (29, 18332): 773.5240408955325, (29, 18333): 776.3678503569755, (29, 18336): 774.4378345035882, (29, 18337): 775.002869188501, (29, 18403): 776.0089817558915, (29, 18432): 755.9031861543805, (29, 18451): 769.4120984234505, (29, 18466): 782.2398545174375, (29, 18481): 770.8289314891052, (29, 18483): 771.1024699081577, (29, 18484): 769.5740286267699, (29, 18485): 764.6992031359887, (29, 18486): 767.2658404183014, (29, 18487): 763.8739115973663, (29, 18489): 767.8185064554428, (29, 18490): 770.1396846593434, (29, 18491): 771.5818705320063, (29, 18492): 761.0179575029687, (29, 18493): 766.4307955158216, (29, 18494): 767.4539458694707, (29, 18495): 769.0243487415399, (29, 18496): 767.7354562416792, (29, 18497): 762.8440384893781, (29, 18498): 764.6496953206569, (29, 18499): 766.998977977922, (29, 18501): 764.8178303237702, (29, 18502): 763.284049678309, (29, 18503): 762.437885432357, (29, 18504): 768.6689342485993, (29, 18506): 764.2655213090063, (29, 18507): 762.651258703581, (29, 18508): 766.4070277949618, (29, 18509): 766.1789353377503, (29, 18510): 762.0966577759772, (29, 18511): 766.3333242207956, (29, 18512): 765.0743089617464, (29, 18515): 768.4229864903323, (29, 18516): 767.6489338285381, (29, 18517): 765.3280731675359, (29, 18518): 769.1234708648755, (29, 18519): 769.15125002752, (29, 18520): 766.2900997180419, (29, 18522): 776.0394006704863, (29, 18523): 776.0549619390513, (29, 18532): 777.6731121702368, (29, 18535): 774.0010751230225, (29, 18537): 771.9577623736848, (29, 18539): 772.2257898430844, (29, 18540): 772.2957725259527, (29, 18541): 773.163899428235, (29, 18542): 773.7443533533846, (29, 18543): 770.7388178421202, (29, 18546): 771.6518642478559, (29, 18555): 774.8332238091234, (29, 18556): 775.2082324105487, (29, 18565): 777.0279473560289, (29, 18567): 777.3677332132157, (29, 18568): 775.8838063784929, (29, 18577): 788.4790854976736, (29, 18583): 787.1835704514596, (29, 18605): 790.8248241574871, (29, 18608): 777.2615305644414, (29, 18616): 802.51919775394, (29, 18618): 811.9837478932583, (29, 18625): 810.735496422466, (29, 18645): 802.8487576483724, (29, 18646): 804.403013940774, (29, 18653): 793.9588032719628, (29, 18654): 801.9088757497503, (29, 18655): 796.2330011100445, (29, 18666): 832.3694333862892, (29, 18837): 837.0681140712642, (29, 18974): 777.393233409684, (29, 18999): 790.1892750047936, (29, 19000): 793.2311476145176, (29, 19174): 686.0464469210938, (29, 19342): 754.5836901238416, (29, 19455): 681.3979968959735, (29, 19555): 566.1039613758377, (29, 19564): 594.7700568434509, (29, 19573): 584.7504048722767, (29, 19586): 578.8899793880881, (29, 19605): 577.5460609270775, (29, 19611): 583.5078404527867, (29, 19614): 575.0712214802808, (29, 19641): 650.1974766099979, (29, 19702): 655.0264140482743, (29, 19713): 648.2190437656296, (29, 19731): 514.363514296255, (29, 19819): 669.9950368220157, (29, 19893): 389.97666784438957, (29, 19899): 432.5595695398719, (29, 19929): 399.60757153127247, (29, 19951): 478.514811715221, (29, 19962): 408.93417218231303, (29, 19970): 420.69066301384, (29, 19971): 422.1887527210122, (29, 19972): 416.4652173318453, (29, 19975): 412.5150109140448, (29, 19978): 489.53035441018477, (29, 19987): 490.1840375249989, (29, 19989): 468.75849462617384, (29, 20039): 493.8068986539202, (29, 20043): 501.8788575811379, (29, 20047): 494.3335422700753, (29, 20052): 471.36890006590954, (29, 20054): 473.5950747810766, (29, 20085): 575.5711687402477, (29, 20104): 582.0745611361101, (29, 20132): 542.8861615428104, (29, 20203): 401.41772842364674, (29, 20280): 399.2221220298117, (29, 20285): 400.03248518943064, (29, 20290): 401.65224302505845, (29, 20297): 393.73940900398924, (29, 20309): 504.58101792578873, (29, 20453): 607.0425179046715, (29, 20485): 344.7532179968935, (29, 20520): 324.5208378023265, (29, 20526): 324.6934941886245, (29, 20698): 972.571221088765, (29, 20868): 1146.0916279436635, (29, 21042): 223.36188348818226, (29, 21057): 261.4313823928246, (29, 21066): 236.43645404946741, (29, 21075): 238.16989598577123, (29, 21093): 217.36036248352684, (29, 21098): 233.52466998075255, (29, 21127): 221.6889579023081, (29, 21130): 224.62117959490027, (29, 21144): 231.6591358433795, (29, 21146): 219.2976632399352, (29, 21147): 233.53062563390674, (29, 21148): 237.10733454755564, (29, 21153): 256.70563650313386, (29, 21293): 277.26765399282294, (29, 21426): 345.58060668087177, (29, 21442): 398.05036577220363, (29, 21451): 402.75909316604924, (29, 21466): 367.128822170307, (29, 21469): 370.8604431141542, (29, 21471): 365.4543098114202, (29, 21473): 367.4784853643896, (29, 21475): 364.5316436099271, (29, 21482): 376.58954774640176, (29, 21484): 374.0422020380272, (29, 21488): 372.74929354008333, (29, 21494): 359.80058270718683, (29, 21498): 363.7868505290316, (29, 21500): 353.7866261695468, (29, 21514): 346.9295182408617, (29, 21537): 342.43325538267567, (29, 21662): 340.3571279340337, (29, 21691): 319.92450167463403, (29, 21757): 324.10423511481116, (29, 21777): 127.56901582575962, (29, 21778): 123.73635982524989, (29, 21779): 120.85945105106327, (29, 21790): 137.42229455409415, (29, 21802): 127.7624961064935, (29, 21824): 127.85359544712189, (29, 21874): 115.93864616982479, (29, 21879): 104.67541467431633, (29, 21983): 171.16078984292244, (29, 22002): 197.5986585698167, (29, 22132): 269.10052605397436, (29, 22261): 813.446061654407, (29, 22298): 800.4896086957049, (29, 22339): 884.111159892934, (29, 22508): 678.6502890266572, (29, 22841): 2312.18940067995, (29, 22842): 2311.9757287884763, (29, 22874): 2294.739877484025, (29, 22941): 2297.259668121889, (29, 22956): 2307.057255003053, (29, 22960): 2310.602150594912, (29, 22968): 2317.0682867245628, (29, 22970): 2320.3100257586434, (29, 22974): 2323.0720102076807, (29, 22980): 2335.073477880478, (29, 23025): 2330.6860239849584, (29, 23028): 2327.342704622085, (29, 23081): 2343.547949038627, (29, 23104): 2316.351775074577, (29, 23147): 2219.4767210725713, (29, 23298): 425.0858031389339, (29, 23376): 406.6040249923915, (29, 23381): 381.6116502075023, (29, 23529): 426.0541764586811, (29, 23556): 416.8317046400603, (29, 23718): 425.9807936667822, (29, 24001): 538.7596634263442, (29, 24094): 555.1298478226465, (29, 24129): 574.2802214908535, (29, 24174): 527.9239960159281, (29, 24235): 566.7082619975175, (29, 24259): 588.9824259907259, (29, 24260): 587.0047871592786, (29, 24261): 583.4443764128702, (29, 24305): 612.578648428066, (29, 24306): 615.4977116009882, (29, 24307): 610.3586435965636, (29, 24308): 599.1912946655426, (29, 24498): 673.3768068398017, (29, 24499): 673.4829947104096, (29, 24500): 670.2954489193752, (29, 24668): 664.6163340161173, (29, 24711): 690.5004064456584, (29, 24756): 698.4994326283503, (29, 24788): 705.942248782802, (29, 24809): 680.0874536121623, (29, 24813): 688.5043654850816, (29, 24821): 685.9015222818059, (29, 24825): 687.1126457635222, (29, 24832): 678.9063440023034, (29, 24833): 682.4304764988606, (29, 24835): 685.7264875800812, (29, 24837): 691.8383835272055, (29, 24840): 678.1042202729186, (29, 24841): 684.082783101895, (29, 24844): 677.9195508414793, (29, 24845): 682.4920759690411, (29, 24846): 680.2785337216405, (29, 24849): 682.0346692942555, (29, 24850): 689.149501801742, (29, 24863): 642.671628633116, (29, 24866): 649.1123499421767, (29, 24885): 655.3935508701882, (29, 24886): 655.1760890629831, (29, 24889): 671.8064625517945, (29, 24903): 678.4386791115671, (29, 24909): 657.3741413725082, (29, 24999): 941.5112108913927, (29, 25019): 937.7353024732979, (29, 25028): 936.9863120806913, (29, 25137): 450.03791903800834, (29, 25145): 455.7311434683025, (29, 25208): 559.8872976075696, (29, 25233): 553.342460906386, (29, 25371): 426.87228031126693, (29, 25377): 402.5693932210519, (29, 25828): 182.17443651544846, (29, 25851): 169.8705181712488, (29, 25874): 160.17659688584405, (29, 25898): 189.8723482474266, (29, 25946): 181.16692847637515, (29, 26047): 256.5750912261067, (29, 26066): 241.8070333163914, (29, 26197): 212.39533462064472, (29, 26212): 361.1333241055468, (29, 26253): 381.2838346449644, (29, 26254): 371.7055079971996, (29, 26257): 370.7372301431104, (29, 26258): 378.96471817990385, (29, 26260): 374.2651216246717, (29, 26266): 368.40635113075666, (29, 26267): 364.80831304312704, (29, 26271): 366.28495887540396, (29, 26304): 289.85998296561894, (29, 26305): 285.8122997742376, (29, 26363): 224.44228189593866, (29, 26441): 852.8842834463832, (29, 26442): 850.6364315272605, (29, 26450): 839.7993515763528, (29, 26459): 839.1081191736419, (29, 26462): 840.7211552003324, (29, 26467): 872.4991781357809, (29, 26471): 863.4883519898349, (29, 26472): 862.518982232555, (29, 26473): 862.1305801631676, (29, 26476): 856.9222360010162, (29, 26485): 844.4153540235293, (29, 26493): 844.6817557135614, (29, 26524): 845.6056106034466, (29, 26525): 844.284765367878, (29, 26556): 859.1976832281778, (29, 26560): 858.334968714695, (29, 26561): 851.5232783088373, (29, 26564): 856.2244093361886, (29, 26569): 849.7760881972486, (29, 26570): 846.9645162004208, (29, 26573): 848.62877009873, (29, 26581): 848.3309269664447, (29, 26583): 845.9844656533393, (29, 26593): 848.3706116709029, (29, 26837): 874.5977793284504, (29, 26844): 881.883086315592, (29, 26863): 865.9707534347764, (29, 26893): 886.8945017666815, (29, 26902): 896.7689984593916, (29, 26905): 886.8114814844153, (29, 26912): 894.5054957430835, (29, 26921): 875.9938616149283, (29, 26922): 856.3319332433505, (29, 27212): 942.0479155405556, (29, 27218): 934.6479922352277, (29, 27239): 955.770089550708, (29, 27257): 948.0066655021816, (29, 27274): 958.3469354172144, (29, 27279): 956.2643551557013, (29, 27282): 948.0425875746604, (29, 27283): 952.3079742442914, (29, 27285): 961.7581729391292, (29, 27286): 953.3281366708347, (29, 27290): 940.9295412508396, (29, 27295): 936.6518904649079, (29, 27300): 959.971306814475, (29, 27344): 935.641054205557, (29, 27366): 944.4761717049512, (29, 27383): 961.4080761270351, (29, 27398): 972.6823982079839, (29, 27406): 964.8856457204603, (29, 27407): 967.7342471480843, (29, 27426): 960.7286932294707, (29, 27432): 924.0503528970881, (29, 27460): 947.5637591625122, (29, 27523): 940.570259663923, (29, 27545): 1094.1894235210261, (29, 27602): 1278.5665450762008, (29, 27606): 1282.4017491055756, (29, 27646): 1080.7885502811962, (29, 27667): 1118.1308936647947, (29, 27672): 1120.292942368028, (29, 27674): 1113.8004558627285, (29, 27688): 1119.9627749130304, (29, 27692): 1126.5200772605378, (29, 27693): 1120.887303876359, (29, 27705): 1120.3682352800538, (29, 27712): 1122.9516943938147, (29, 27786): 1298.3292216646616, (29, 27790): 1282.1393430590622, (29, 27791): 1281.1076077937453, (29, 27795): 1287.5172837384985, (29, 27801): 1274.9528882364339, (29, 27813): 1303.5522965757216, (29, 27816): 1297.6573433632575, (29, 27823): 1274.5254995228274, (29, 27830): 1290.4994358569384, (29, 27884): 1016.1632063225661, (29, 27885): 1064.7376108322985, (29, 27896): 1035.470785959954, (29, 27919): 1033.672010704881, (29, 27922): 1039.4009849437218, (29, 27930): 1023.8007876777549, (29, 27934): 1025.4750270645336, (29, 27935): 1026.6392193908455, (29, 27948): 1250.5586629451368, (29, 27951): 1263.0314809429033, (29, 28061): 1084.3466589589696, (29, 28290): 1470.7046196714914, (29, 28292): 1478.9285608644993, (29, 28293): 1472.3177683956558, (29, 28295): 1469.0680649872938, (29, 28296): 1470.3574133956442, (29, 28297): 1466.3611876107582, (29, 28302): 1463.6096506199376, (29, 28310): 1655.2507757434512, (29, 28313): 1663.5432074650976, (29, 28372): 1660.4486355097465, (29, 28398): 1661.3889887730822, (29, 28399): 1659.0755585344098, (29, 28400): 1663.3677120225873, (29, 28401): 1651.5826950080886, (29, 28445): 1661.0030506707114, (29, 28475): 1640.0958119860454, (29, 28885): 543.6967595980555, (29, 28886): 539.1964191763071, (29, 28915): 539.0713309795386, (29, 28916): 537.0026851400108, (29, 28917): 534.3242058748414, (29, 28921): 551.2396348554023, (29, 28931): 549.3349558799317, (29, 28945): 520.945566469548, (29, 28982): 528.4899325302641, (29, 29219): 537.2774428495989, (29, 29228): 521.2840602373205, (29, 29246): 622.81235786663, (29, 29248): 620.860264775273, (29, 29282): 599.1626865420103, (29, 29290): 634.1914367716498, (29, 29291): 629.6251504777498, (29, 29292): 633.7863060139703, (29, 29293): 625.3415799645472, (29, 29294): 631.745307363508, (29, 29298): 625.7725155101847, (29, 29299): 624.8541238609027, (29, 29304): 617.4260257050316, (29, 29317): 597.5661236550395, (29, 29323): 596.0628653917001, (29, 29330): 605.5587017641392, (29, 29331): 610.5057401547123, (29, 29344): 536.5232080203435, (29, 29445): 348.48735634602775, (29, 29724): 2290.8499336139953, (29, 29738): 2294.034447517724, (29, 29745): 2284.9755023817625, (29, 29748): 2287.9961071259704, (29, 29750): 2293.705543291223, (29, 29759): 2283.4833239127224, (29, 29772): 2295.2728389408426, (29, 29781): 2292.733179664829, (29, 29784): 2290.2042892131535, (29, 29790): 2295.510322074134, (29, 29811): 2289.3325461379254, (29, 29817): 2314.324993078302, (29, 29818): 2311.8767957162527, (29, 29929): 2283.1317200043914, (29, 30039): 2321.465628973673, (29, 30066): 2292.8269656652105, (29, 30116): 2186.8357996002014, (29, 30238): 2029.8883349199307, (29, 30248): 2103.5692332618582, (29, 30260): 2105.026669103659, (29, 30545): 502.2807157942002, (29, 30733): 353.2939351586528, (29, 30756): 279.7379668171501, (29, 30921): 368.25219799500024, (29, 31079): 472.93128286826015, (29, 31149): 420.3318299629795, (29, 31154): 429.1014475807551, (29, 31160): 419.19380140586674, (29, 31163): 429.0551323870369, (29, 31189): 416.76754197780207, (29, 31215): 424.78569015237935, (29, 31259): 463.41262965324495, (29, 31262): 460.67838523371296, (29, 31430): 500.44599220720926, (29, 31568): 572.0842097275344, (29, 31751): 488.677221929927, (31, 109): 2127.9822507540403, (31, 872): 425.47089192497333, (31, 873): 417.21408051180003, (31, 877): 418.16662384111504, (31, 879): 416.732094366867, (31, 884): 420.4292386903157, (31, 889): 416.1856387170718, (31, 891): 423.7259803251962, (31, 892): 410.7626421324797, (31, 894): 412.6878027066951, (31, 896): 424.2552393832248, (31, 903): 415.4513360797095, (31, 909): 436.5143009269927, (31, 910): 435.25033967587984, (31, 912): 440.2094613240937, (31, 913): 444.94800586783856, (31, 916): 449.89873339085915, (31, 926): 435.28419817113536, (31, 927): 438.5018033793062, (31, 948): 427.0680148385742, (31, 961): 430.75753933676873, (31, 962): 431.2448764510019, (31, 963): 431.3477529752235, (31, 967): 412.79730878524737, (31, 974): 412.45002895909766, (31, 998): 407.79290765341335, (31, 1014): 266.1874968187636, (31, 1086): 513.7667635510437, (31, 1087): 524.4137899854777, (31, 1089): 526.1972292255667, (31, 1090): 522.2547068554421, (31, 1092): 511.47588318896373, (31, 1097): 517.7915853548441, (31, 1107): 512.397163721531, (31, 1387): 1733.8887176114522, (31, 1554): 1841.1254356326908, (31, 1827): 0.3588578804051198, (31, 1828): 2.1012462280347135, (31, 1829): 1.835426849679208, (31, 1830): 9.23316880836397, (31, 1831): 7.789407171067885, (31, 1832): 6.484259976872661, (31, 1833): 4.839473669132221, (31, 1836): 2.6761332317557187, (31, 1841): 8.219150805240774, (31, 1843): 6.556415207561416, (31, 1844): 8.750661510117514, (31, 1845): 8.730041863415646, (31, 1847): 7.627566028831592, (31, 1848): 5.335030623804841, (31, 1849): 14.480123613104986, (31, 1850): 14.820690279397311, (31, 1851): 8.627404907522637, (31, 1852): 12.46269228770157, (31, 1854): 9.940120017516987, (31, 1856): 10.03765253785739, (31, 1857): 6.727227912683443, (31, 1858): 11.07087961359369, (31, 1861): 3.451194357140226, (31, 1866): 12.429302068419684, (31, 1867): 6.017366826033481, (31, 1868): 3.1773015100488697, (31, 1870): 13.350892984027976, (31, 1871): 4.533106996484502, (31, 1875): 7.2730498827579195, (31, 1880): 7.058466235857967, (31, 1882): 10.82608077854826, (31, 1883): 12.230016458378255, (31, 1889): 5.146871344618265, (31, 1893): 6.822479079556132, (31, 1894): 8.363537255270964, (31, 1899): 8.531541779367823, (31, 1900): 8.071596095260988, (31, 1902): 7.664411861989653, (31, 1905): 8.418054529152142, (31, 1907): 2.6822990887631732, (31, 1910): 5.257136683164693, (31, 1917): 18.681187657752343, (31, 1920): 4.5849774797143565, (31, 1935): 12.554578265025011, (31, 1937): 12.965488731246527, (31, 1946): 19.433334809740344, (31, 1949): 19.21734068912495, (31, 1950): 20.077856031766505, (31, 1951): 17.3362353641407, (31, 1952): 9.855426100781333, (31, 1953): 12.562089241247435, (31, 1954): 10.917135625744514, (31, 1958): 16.12846164378417, (31, 1960): 10.69686786330085, (31, 1968): 8.67266848360436, (31, 1969): 18.89525860541531, (31, 1974): 14.872424339094035, (31, 1975): 12.576447748020538, (31, 1979): 17.512996378156128, (31, 1980): 10.06785015982524, (31, 1981): 14.444195103681075, (31, 1985): 16.37929937728237, (31, 1994): 21.78379525873166, (31, 2011): 13.156526767764705, (31, 2019): 32.29751375604847, (31, 2020): 29.136960133114915, (31, 2029): 25.621814597378236, (31, 2030): 26.888130506658456, (31, 2032): 29.235986713153178, (31, 2033): 26.547993228262296, (31, 2034): 30.1384252930217, (31, 2036): 43.34526334677267, (31, 2037): 39.07342632650549, (31, 2038): 21.779397620108746, (31, 2042): 46.32822860823722, (31, 2050): 20.420650399923428, (31, 2051): 24.07712773928978, (31, 2053): 22.84162934202252, (31, 2054): 24.79656446339403, (31, 2066): 21.81759272548983, (31, 2067): 19.78469185152624, (31, 2071): 26.382186034959844, (31, 2072): 20.89893775627683, (31, 2073): 38.227685427992625, (31, 2074): 38.15969786840088, (31, 2080): 46.20906671550053, (31, 2082): 18.007247032221645, (31, 2083): 15.165598343766149, (31, 2089): 21.45497227555732, (31, 2090): 19.271793363888758, (31, 2092): 23.679123373487457, (31, 2098): 43.703177486062174, (31, 2099): 39.85965016195493, (31, 2101): 43.47095859834266, (31, 2102): 29.346956646530902, (31, 2103): 33.37802736927128, (31, 2104): 35.40175091839146, (31, 2106): 13.520373573973025, (31, 2112): 41.01038274845021, (31, 2113): 26.736584746308807, (31, 2114): 22.249080363398015, (31, 2117): 12.408186168272744, (31, 2123): 138.3944712736939, (31, 2124): 137.89639969375295, (31, 2134): 130.51835900140853, (31, 2138): 132.36730665831556, (31, 2141): 133.03568010765463, (31, 2148): 97.41543340621257, (31, 2150): 133.22802847112646, (31, 2151): 129.85288375767337, (31, 2152): 131.39215198523326, (31, 2153): 100.4006839063324, (31, 2154): 106.49015073975335, (31, 2155): 101.53190908631441, (31, 2156): 106.3830741496065, (31, 2157): 85.48056945479982, (31, 2160): 114.62974947640663, (31, 2161): 128.1953971585949, (31, 2162): 87.30628025223594, (31, 2163): 89.83243892152676, (31, 2164): 87.9159554497366, (31, 2168): 115.48263838565354, (31, 2172): 99.23300158604705, (31, 2174): 125.64046988752808, (31, 2178): 93.88814531532267, (31, 2179): 93.36601609341427, (31, 2183): 128.3110754506628, (31, 2185): 126.0958253791779, (31, 2186): 127.69264652397071, (31, 2190): 118.41332537888876, (31, 2192): 120.4681942884882, (31, 2193): 129.39090704811196, (31, 2194): 131.52639882716304, (31, 2195): 127.2031580550671, (31, 2197): 117.72092581831551, (31, 2205): 114.3541891151526, (31, 2207): 112.12671505377392, (31, 2208): 112.37254989733009, (31, 2212): 139.11956132730901, (31, 2214): 138.20214483667527, (31, 2225): 121.41256055432979, (31, 2231): 206.34501718115916, (31, 2278): 65.45533923432187, (31, 2284): 54.11739225644481, (31, 2285): 54.83939402336859, (31, 2291): 72.97808156782295, (31, 2292): 72.12271270649295, (31, 2307): 60.04158639882159, (31, 2313): 76.39364779183155, (31, 2317): 81.77152974416536, (31, 2319): 68.41896086064288, (31, 2321): 63.501003378974346, (31, 2323): 65.3055097163777, (31, 2326): 53.8029918530834, (31, 2327): 57.675206924888734, (31, 2329): 60.013173423037806, (31, 2330): 62.053403552356876, (31, 2332): 54.28384312781782, (31, 2344): 68.49147852257632, (31, 2346): 66.55372828558116, (31, 2361): 92.56461916819475, (31, 2368): 39.24037276131454, (31, 2374): 33.228889454720296, (31, 2375): 34.83569719921177, (31, 2377): 47.49138362395366, (31, 2378): 31.500209763428543, (31, 2379): 26.47510339534662, (31, 2380): 29.27350202365572, (31, 2383): 47.37194494338571, (31, 2385): 47.492644584569625, (31, 2395): 51.44160524587958, (31, 2397): 25.269990230955187, (31, 2398): 51.553245125764285, (31, 2399): 49.43503557736312, (31, 2400): 50.39416689824567, (31, 2402): 32.23865162045355, (31, 2403): 29.509829922735154, (31, 2404): 30.67382027112611, (31, 2405): 35.73918167206849, (31, 2407): 34.16446892581272, (31, 2408): 29.387751135753852, (31, 2409): 34.72175961798367, (31, 2411): 22.58666518017558, (31, 2412): 25.84979491645436, (31, 2413): 22.555257262551784, (31, 2414): 25.61345891711494, (31, 2422): 21.388465182952544, (31, 2424): 26.562305007481086, (31, 2426): 27.43237180271246, (31, 2433): 30.110697160934095, (31, 2436): 27.88307527024692, (31, 2437): 48.68321428157012, (31, 2440): 44.87085181022772, (31, 2445): 69.63230703856068, (31, 2447): 56.16617317475133, (31, 2454): 65.79422911593622, (31, 2455): 63.86497610053274, (31, 2460): 39.33495121585854, (31, 2461): 42.549411117574806, (31, 2471): 115.31513641046696, (31, 2492): 213.10389921024864, (31, 2511): 178.36441175604773, (31, 2523): 196.05492379383145, (31, 2525): 203.1255655867504, (31, 2535): 123.56197245734164, (31, 2537): 124.11938160285737, (31, 2538): 119.72780190611584, (31, 2539): 138.74716432184337, (31, 2540): 123.93858253960043, (31, 2542): 130.7136673369872, (31, 2559): 157.17259095011178, (31, 2575): 166.91693822242783, (31, 2599): 64.743438392918, (31, 2600): 66.97504044100614, (31, 2607): 50.02984540635854, (31, 2627): 251.82163262360118, (31, 2647): 270.6961660513541, (31, 2674): 246.6248817367826, (31, 2681): 256.0364414546201, (31, 2683): 254.28967237489388, (31, 2686): 246.1033410807149, (31, 2689): 314.26309012967505, (31, 2690): 316.89873490689445, (31, 2713): 399.5481444811104, (31, 2714): 410.0849842780869, (31, 2715): 411.4752726512318, (31, 2739): 407.508971471124, (31, 2740): 372.9467802757919, (31, 2741): 371.78523083203646, (31, 2749): 415.3911051300035, (31, 2750): 412.5168237322847, (31, 2752): 412.00266120514044, (31, 2755): 415.18951484800453, (31, 2758): 417.6360000855605, (31, 2759): 416.1595906998558, (31, 2769): 410.7769763068399, (31, 2771): 381.93188173664413, (31, 2779): 406.50586150190315, (31, 2784): 402.738636279754, (31, 2800): 429.5208823826797, (31, 2802): 383.19991973028596, (31, 2803): 379.6400751000993, (31, 2804): 377.52307579422154, (31, 2805): 393.53520502703003, (31, 2807): 390.3698884947577, (31, 2809): 396.7409642223351, (31, 2812): 380.4792618249365, (31, 2814): 416.7491330335318, (31, 2817): 444.7769675612959, (31, 2819): 383.024253567201, (31, 2823): 408.24604404989316, (31, 2832): 399.61028228500516, (31, 2836): 393.0663542268986, (31, 2839): 387.2287245970772, (31, 2841): 431.0024016243176, (31, 2843): 425.58251841535923, (31, 2846): 406.83286793180946, (31, 2849): 405.8406080303015, (31, 2852): 402.3550813996438, (31, 2853): 407.63736657918025, (31, 2876): 422.623369489845, (31, 2877): 430.1571265714143, (31, 2885): 460.8253438372817, (31, 2918): 364.2370585189923, (31, 2921): 370.3416628624904, (31, 2925): 331.9539861745791, (31, 2926): 313.50819189880997, (31, 2930): 370.935821582495, (31, 2931): 341.4406333736484, (31, 2938): 369.5693089903736, (31, 2940): 352.35280808513795, (31, 2947): 336.7486325321534, (31, 2949): 358.782039090911, (31, 2950): 365.1156292222091, (31, 2952): 364.0695727918032, (31, 2958): 361.67366933699867, (31, 2959): 356.77015761436337, (31, 2960): 361.5330690123781, (31, 2961): 362.6060487029754, (31, 2963): 363.7123757858181, (31, 2968): 367.59468578963185, (31, 2976): 360.20202548066885, (31, 2981): 379.6062796917396, (31, 2982): 385.64605210967954, (31, 2984): 386.354194396941, (31, 3003): 392.2061286781788, (31, 3046): 308.38735367070177, (31, 3050): 351.0151564184059, (31, 3051): 349.1354334868912, (31, 3053): 350.2226887060574, (31, 3069): 370.87588618441896, (31, 3071): 334.9247074286502, (31, 3080): 471.32964692516657, (31, 3199): 429.6428283850886, (31, 3200): 432.6725977276843, (31, 3205): 438.2842183445535, (31, 3209): 434.10887689225854, (31, 3215): 429.16058867016324, (31, 3217): 428.5620936067693, (31, 3249): 425.4403449805402, (31, 3263): 431.5345409036468, (31, 3289): 417.1631465970346, (31, 3301): 426.6832375619407, (31, 3302): 422.93376195608937, (31, 3307): 421.55841985100636, (31, 3310): 427.09444300849367, (31, 3391): 605.3219227189587, (31, 3509): 989.2680916100708, (31, 3510): 993.680485659931, (31, 3511): 989.7672594179354, (31, 3512): 991.6673227210209, (31, 3514): 989.9930058350978, (31, 3519): 984.0474019305517, (31, 3536): 979.7595925640236, (31, 3545): 971.8468204157151, (31, 3548): 977.4143738870409, (31, 3572): 978.4401960652174, (31, 3581): 987.1648842460752, (31, 3583): 986.0323450587966, (31, 3601): 977.5802161599092, (31, 3656): 989.0640903704868, (31, 3669): 1007.7905384722646, (31, 3670): 1004.4391505919508, (31, 3695): 1021.9269285220727, (31, 3696): 1018.7052632742824, (31, 3782): 962.6969999519464, (31, 3792): 969.2942318453191, (31, 3989): 2948.0284571559514, (31, 4008): 2972.298973716788, (31, 4031): 2969.0141361885153, (31, 4045): 2962.0318456520804, (31, 4144): 2964.8872593099377, (31, 4145): 2942.0628302908312, (31, 4164): 2955.883539947481, (31, 4168): 2949.040114726673, (31, 4173): 2947.8527189943325, (31, 4181): 2933.0122632451044, (31, 4228): 2917.338855106115, (31, 4248): 2913.444089501925, (31, 4254): 2784.6282979930515, (31, 4260): 2784.7355088554623, (31, 4262): 2793.6623565426103, (31, 4273): 2791.520842218513, (31, 4319): 2710.531135989672, (31, 4326): 2707.757840323385, (31, 4328): 2708.8008698280396, (31, 4334): 2714.0772679696947, (31, 4335): 2712.110041262752, (31, 4372): 2524.8863863177753, (31, 4413): 2589.300374738104, (31, 4434): 2523.6689833193773, (31, 4447): 2538.1910846399737, (31, 4452): 2523.8209083680044, (31, 4463): 2344.661072313188, (31, 4465): 2351.75597242572, (31, 4619): 2580.125873578507, (31, 4645): 2600.170050634219, (31, 4657): 2595.191518470487, (31, 4666): 2586.453140606229, (31, 4676): 2598.5961325264134, (31, 4678): 2602.3764797187596, (31, 4689): 2591.4112341074774, (31, 4704): 2651.3253239012574, (31, 4726): 2745.522865590565, (31, 4727): 2743.5588962079314, (31, 4730): 2739.927580963719, (31, 4731): 2739.8026289887157, (31, 4734): 2748.613767050601, (31, 4735): 2745.749435850075, (31, 4736): 2745.818669833076, (31, 4737): 2741.33022144236, (31, 4738): 2741.067450641209, (31, 4756): 2742.49718190395, (31, 4760): 2737.5446860274305, (31, 4761): 2740.626089809268, (31, 4762): 2733.6615588583845, (31, 4765): 2737.9236493091253, (31, 4773): 2750.369016913544, (31, 4774): 2746.926949378784, (31, 4790): 2749.3154361548745, (31, 4795): 2748.0206323238313, (31, 4799): 2746.8825335805946, (31, 4801): 2748.687531973731, (31, 4804): 2750.798438919075, (31, 4805): 2749.708870201983, (31, 4806): 2743.6902605498617, (31, 4815): 2740.3202079022144, (31, 4816): 2746.0125907522947, (31, 4817): 2745.0392353200655, (31, 4826): 2742.7058482332523, (31, 4830): 2739.0829094368087, (31, 4839): 2743.176903432599, (31, 4840): 2744.1035621774968, (31, 4841): 2739.2858689783316, (31, 4846): 2738.249393946469, (31, 4848): 2736.1344921304767, (31, 4850): 2737.636714878555, (31, 4871): 2722.4461909977563, (31, 4883): 2737.7530061995317, (31, 4900): 2732.212023416882, (31, 4901): 2728.441389557164, (31, 4917): 2546.9363513571175, (31, 4931): 2530.6926901333422, (31, 4944): 2550.033037595133, (31, 4956): 2532.418026803343, (31, 4958): 2529.4683684806387, (31, 4959): 2524.6850274778526, (31, 4961): 2536.7192707417844, (31, 4966): 2527.012218207477, (31, 5207): 2508.768940964242, (31, 5272): 2281.24414282664, (31, 5283): 2286.231046211013, (31, 5287): 2288.5811195063366, (31, 5289): 2290.5617301209427, (31, 5293): 2287.6529568707197, (31, 5295): 2302.4245553532683, (31, 5296): 2298.901404955671, (31, 5298): 2296.817729553841, (31, 5303): 2298.255192438342, (31, 5305): 2271.5374184350403, (31, 5306): 2262.5744146376287, (31, 5307): 2268.523976801737, (31, 5308): 2272.8269302274302, (31, 5313): 2276.943095274053, (31, 5314): 2281.5496495550774, (31, 5317): 2270.611415295535, (31, 5319): 2292.336514555822, (31, 5324): 2291.97835251914, (31, 5326): 2291.9481199065117, (31, 5348): 2258.384539802514, (31, 5351): 2257.4165791530017, (31, 5399): 2288.5232586035245, (31, 5413): 2256.4413955252026, (31, 5422): 2294.800101164758, (31, 5445): 2281.1583025165273, (31, 5448): 2276.058336190547, (31, 5456): 2271.208900867246, (31, 5467): 2274.97696594403, (31, 5624): 2230.8547016827924, (31, 5671): 2442.772556391423, (31, 5672): 2436.128290864067, (31, 5797): 2524.974659997858, (31, 5871): 2328.4119990786958, (31, 5976): 2265.897069202582, (31, 6118): 729.8684709857281, (31, 6248): 793.6895659085022, (31, 6345): 2039.8409175401578, (31, 6352): 2020.4422099365995, (31, 6354): 2044.0353569882466, (31, 6359): 2048.8613958169667, (31, 6376): 2026.0188726421538, (31, 6378): 2041.8437025297517, (31, 6381): 2047.964189785233, (31, 6383): 2035.3226003839845, (31, 6396): 2049.7968470748965, (31, 6399): 2041.2939278338722, (31, 6408): 2020.1279857603238, (31, 6409): 2026.6550322213918, (31, 6419): 1991.1501254938044, (31, 6422): 2020.6016860650516, (31, 6423): 2018.8860133469555, (31, 6424): 2039.2433441381556, (31, 6439): 2034.6866744477795, (31, 6464): 2028.4932366133646, (31, 6465): 2027.4081677984352, (31, 6469): 2031.6954315867658, (31, 6470): 2030.9354500341544, (31, 6472): 2055.834083952185, (31, 6480): 2047.5730566784641, (31, 6486): 2055.049662105667, (31, 6497): 2052.3021899622913, (31, 6503): 2024.9971942109337, (31, 6508): 2028.9246514174097, (31, 6509): 2031.5647880296403, (31, 6521): 2048.210244960403, (31, 6544): 2044.4334932343704, (31, 6552): 2019.5159502382487, (31, 6553): 2016.2058074540864, (31, 6554): 2012.8713058599503, (31, 6578): 2025.4112606891044, (31, 6582): 2020.4460924103475, (31, 6601): 2026.3715621914544, (31, 6609): 2055.123143596549, (31, 6610): 2055.4959367675706, (31, 6611): 2057.5531474972536, (31, 6614): 2056.7314256077266, (31, 6615): 2056.8248811334847, (31, 6616): 2058.3455134944575, (31, 6617): 2057.514191256241, (31, 6618): 2060.431682898078, (31, 6619): 2054.0998464489876, (31, 6620): 2057.546994591901, (31, 6621): 2054.6242144979137, (31, 6622): 2055.866905741393, (31, 6623): 2055.4649625081033, (31, 6624): 2052.096335515747, (31, 6625): 2052.0565375325314, (31, 6626): 2054.3378684175145, (31, 6627): 2056.8425655434307, (31, 6628): 2056.101304290988, (31, 6629): 2051.78522413069, (31, 6630): 2051.124892392049, (31, 6632): 2051.987913585718, (31, 6634): 2047.5870304223079, (31, 6635): 2054.1050045593993, (31, 6636): 2058.1983652925305, (31, 6637): 2047.9168654924226, (31, 6638): 2050.6094076081604, (31, 6639): 2056.6007521810366, (31, 6640): 2051.522128752567, (31, 6641): 2053.8798777501584, (31, 6642): 2050.0823281748453, (31, 6643): 2054.6683320348898, (31, 6645): 2054.0783497555276, (31, 6646): 2060.12307597235, (31, 6647): 2051.237233168205, (31, 6653): 2056.975426887287, (31, 6655): 2056.924209817688, (31, 6658): 2047.034511751797, (31, 6662): 2049.2933502672263, (31, 6819): 1880.5491920171414, (31, 6996): 1923.3116123954362, (31, 7059): 1961.046726480324, (31, 7187): 1879.7963380478056, (31, 7304): 1807.760925905455, (31, 7528): 1911.8489371416802, (31, 7720): 2142.659302261181, (31, 7793): 2135.3550339326316, (31, 7807): 2139.2897870955926, (31, 7808): 2133.6473489156942, (31, 7831): 2069.4469604337896, (31, 7850): 2108.9097130656187, (31, 7852): 2101.9481494284746, (31, 8012): 2136.1502182514296, (31, 8125): 2150.9665981845487, (31, 8208): 2211.519892380196, (31, 8392): 2085.5305940543435, (31, 8651): 1700.3707215975896, (31, 9088): 1885.9350094790227, (31, 9443): 1579.002879024193, (31, 9444): 1584.1260591513715, (31, 9828): 1404.6162899737174, (31, 9868): 1406.139051276566, (31, 10180): 2153.702914228166, (31, 10256): 2250.116550567309, (31, 10276): 2207.364759020476, (31, 10378): 2225.6931660473147, (31, 10676): 2113.376086019284, (31, 10714): 2047.5676974184908, (31, 10730): 2064.8114601012403, (31, 10862): 1957.9753560855943, (31, 10881): 1972.899947887326, (31, 10883): 1970.5378155411977, (31, 10885): 1954.9472707127184, (31, 10891): 1966.8727995949494, (31, 10909): 1967.2453069055425, (31, 10911): 1971.0709841679247, (31, 10913): 1967.0671830414465, (31, 10915): 1967.8063955149835, (31, 10919): 1970.6337080682927, (31, 11037): 1849.4223166585966, (31, 11039): 1819.3751009469079, (31, 11516): 3184.7713910396437, (31, 11856): 2716.454938963242, (31, 11857): 2712.247623312248, (31, 11861): 2714.4754817455478, (31, 11881): 2711.053999740685, (31, 11902): 2694.087917420386, (31, 11911): 2691.5613573645282, (31, 11914): 2693.6825603112547, (31, 11922): 2706.0999457728612, (31, 11924): 2710.2395647418434, (31, 11926): 2705.3847400361788, (31, 11950): 2715.6099281708266, (31, 11963): 2731.4929768751895, (31, 11983): 2721.4618330012436, (31, 11985): 2739.4169326611823, (31, 12009): 2736.966246188017, (31, 12010): 2725.5360775500358, (31, 12018): 2727.4802945157053, (31, 12020): 2730.44992939648, (31, 12021): 2732.388248824172, (31, 12024): 2743.1693784783756, (31, 12025): 2739.3939495300183, (31, 12027): 2736.873881498026, (31, 12031): 2723.6455095835668, (31, 12032): 2727.2948169908, (31, 12035): 2736.3906083006714, (31, 12041): 2740.3628646037214, (31, 12045): 2591.1266596025785, (31, 12145): 2660.915137012884, (31, 12275): 2955.514184539123, (31, 12294): 2926.300618068155, (31, 12358): 3015.94764315345, (31, 12463): 3050.592114600127, (31, 12465): 3049.546980211129, (31, 12482): 3064.882928287245, (31, 12503): 3062.7458219455184, (31, 12506): 3066.8976079930667, (31, 12549): 3057.946882003757, (31, 12559): 3054.7776273315417, (31, 12569): 3058.1689123122565, (31, 12572): 3061.290801489295, (31, 12574): 3054.7706237045636, (31, 12576): 3061.55431108467, (31, 12591): 3060.8004077783276, (31, 12608): 3085.9659185363594, (31, 12696): 3045.5948579061737, (31, 12710): 3069.1115573613074, (31, 12728): 3057.685734325739, (31, 12766): 2376.8009779123818, (31, 12771): 2344.983714716313, (31, 12790): 2340.856477489005, (31, 12795): 2331.483560374403, (31, 12797): 2290.9465031235745, (31, 12798): 2296.3989287503055, (31, 12811): 2328.347495829742, (31, 12830): 2317.803727078494, (31, 12848): 2323.0467221998865, (31, 12850): 2325.5439922459955, (31, 12852): 2316.1857581391714, (31, 12854): 2311.2873575832477, (31, 12859): 2327.83496585951, (31, 12861): 2301.7473612970757, (31, 12865): 2334.5055943392254, (31, 12866): 2331.8873185129355, (31, 12867): 2341.785700991185, (31, 12874): 2336.998180045076, (31, 12875): 2340.6614455899567, (31, 12881): 2325.580382246526, (31, 12883): 2331.6254023132374, (31, 12885): 2343.8997326776666, (31, 12888): 2328.752170749296, (31, 12889): 2327.3192408101336, (31, 12892): 2338.0871432659483, (31, 12893): 2329.0437937987936, (31, 12896): 2331.8921288241763, (31, 12906): 2337.6450478517577, (31, 13018): 2296.3623086462353, (31, 13071): 2297.600059481149, (31, 13131): 2255.734845783836, (31, 13146): 2287.342861931609, (31, 13159): 2246.885496044878, (31, 13193): 2249.289197279329, (31, 13198): 2191.694161817365, (31, 13292): 2256.1924396694894, (31, 13296): 2273.5559933169216, (31, 13406): 2158.937728728288, (31, 13407): 2157.311619491989, (31, 13417): 2154.912790597237, (31, 13418): 2161.2996602214357, (31, 13438): 2184.4637814871967, (31, 13442): 2188.7608982147926, (31, 13443): 2184.0977250759342, (31, 13764): 1803.117329526625, (31, 13766): 1808.9613938257205, (31, 13771): 1805.3344096664407, (31, 13783): 1794.8388096655633, (31, 13784): 1814.4571451053037, (31, 13792): 1797.3024628249061, (31, 13824): 1791.2227810231766, (31, 14017): 1814.9063118271777, (31, 14870): 1994.0194764664634, (31, 14997): 1850.7394919872622, (31, 15000): 1851.4893484348943, (31, 15003): 1855.762963643343, (31, 15006): 1864.344021897506, (31, 15007): 1868.4970205394636, (31, 15056): 1868.3536135842587, (31, 15063): 1864.7438207556766, (31, 15069): 1863.5627252008896, (31, 15076): 1869.2294244837294, (31, 15086): 1856.0953176980909, (31, 15087): 1851.7582168166027, (31, 15111): 1839.2287698425023, (31, 15116): 1846.4280867193636, (31, 15722): 1736.77405556801, (31, 15998): 1667.9358749832209, (31, 16073): 1134.6419339327326, (31, 16939): 272.73677167540717, (31, 16940): 277.7117589772298, (31, 16951): 276.5084231255705, (31, 16963): 274.8962572563173, (31, 16965): 267.0529689414191, (31, 16969): 271.4447037269094, (31, 16970): 271.17020796458445, (31, 16971): 278.0716099483384, (31, 16973): 280.18528149278745, (31, 16974): 265.52864182723624, (31, 16976): 269.6223035116845, (31, 16978): 274.12173080419876, (31, 16980): 265.7535592687714, (31, 16982): 267.43289465541227, (31, 17045): 461.0052163868512, (31, 17048): 461.1356223302607, (31, 17304): 2879.748653792698, (31, 17305): 2875.043171252093, (31, 17330): 2879.2027568884214, (31, 17334): 2871.6321118089695, (31, 17343): 2885.250713850136, (31, 17345): 2870.814834096401, (31, 17347): 2878.2864950016883, (31, 17351): 2860.4920427145075, (31, 17372): 2870.525173232465, (31, 17373): 2884.849375067197, (31, 17377): 2885.811615124606, (31, 17382): 2876.3750845837335, (31, 17383): 2878.304428091207, (31, 17389): 2872.691624773532, (31, 17400): 2882.384959281925, (31, 17401): 2882.2785228424937, (31, 17402): 2882.893188116144, (31, 17403): 2883.791946584918, (31, 17440): 2870.801397708946, (31, 17455): 2883.243525855388, (31, 17491): 2883.73200289855, (31, 17507): 2867.047649772113, (31, 17509): 2872.436168554658, (31, 17590): 2856.3819245090785, (31, 17615): 2829.976099196391, (31, 17642): 2835.082726724252, (31, 17643): 2834.470083819243, (31, 17668): 2829.852892745096, (31, 17721): 2818.1342827557737, (31, 17754): 2868.2427624907314, (31, 17769): 2869.291373121556, (31, 17776): 2847.4464268487222, (31, 17804): 2877.9542297393564, (31, 17809): 2883.2634560315164, (31, 17824): 2880.0633968287566, (31, 17837): 2863.3555316830602, (31, 17838): 2863.653581743886, (31, 17862): 2859.572155005596, (31, 17866): 2870.997514081719, (31, 17872): 2855.9367733776267, (31, 17873): 2847.144573337686, (31, 17881): 2860.592159595689, (31, 17947): 780.1803466380074, (31, 17951): 789.3062000091109, (31, 17953): 792.2696137108975, (31, 17954): 792.4333763992325, (31, 17959): 779.9364006951749, (31, 17963): 781.1529503418026, (31, 18000): 832.6613665241032, (31, 18001): 832.0050465091472, (31, 18111): 791.6804352576955, (31, 18148): 1010.6175757182008, (31, 18166): 931.0579319008506, (31, 18189): 840.1725605399589, (31, 18239): 2887.744011678411, (31, 18240): 2887.591067981036, (31, 18245): 2888.1938590300665, (31, 18247): 2886.9364759892615, (31, 18251): 2888.064361607035, (31, 18256): 2889.1814824251687, (31, 18258): 2887.7969215018466, (31, 18259): 2887.9878212131157, (31, 18260): 2888.4362354521763, (31, 18262): 2889.355893317997, (31, 18263): 2889.479168210189, (31, 18264): 2889.931115008877, (31, 18266): 2889.6689517374393, (31, 18267): 2890.1236196849804, (31, 18268): 2890.3126032666187, (31, 18269): 2891.208406020842, (31, 18275): 2890.7854051331997, (31, 18285): 2889.8133857345897, (31, 18308): 2880.3407360834512, (31, 18313): 2876.8759702328994, (31, 18314): 2878.18539685514, (31, 18315): 2891.4183092738513, (31, 18316): 2891.217259955363, (31, 18317): 2891.628543346351, (31, 18320): 2892.195463881085, (31, 18321): 2892.365667166257, (31, 18322): 2893.0389373548323, (31, 18324): 2893.764779832304, (31, 18325): 2896.03163379861, (31, 18326): 2895.1927874267194, (31, 18327): 2891.9006990093594, (31, 18329): 2897.1879738655252, (31, 18330): 2895.668076506327, (31, 18331): 2894.2125570468415, (31, 18332): 2892.64881239828, (31, 18333): 2895.5428021911125, (31, 18336): 2894.456218162964, (31, 18337): 2895.3051531055125, (31, 18403): 2893.4553613432035, (31, 18432): 2858.68891615516, (31, 18451): 2882.275095404121, (31, 18466): 2905.3781204691004, (31, 18481): 2892.3297322255403, (31, 18483): 2892.244972056405, (31, 18484): 2891.061464709093, (31, 18485): 2887.5784275671, (31, 18486): 2891.2110546719464, (31, 18487): 2888.402137863075, (31, 18489): 2890.5921882405314, (31, 18490): 2893.7069130648215, (31, 18491): 2895.073897495086, (31, 18492): 2885.4151846532886, (31, 18493): 2890.8184589156594, (31, 18494): 2889.9715348539803, (31, 18495): 2892.700114477863, (31, 18496): 2891.2023275660554, (31, 18497): 2887.826499459974, (31, 18498): 2888.1762682404355, (31, 18499): 2890.2757630209703, (31, 18501): 2888.8947677045094, (31, 18502): 2887.5599326875817, (31, 18503): 2886.441031631474, (31, 18504): 2891.670324050633, (31, 18506): 2889.317297881089, (31, 18507): 2888.0869532930587, (31, 18508): 2890.059645140914, (31, 18509): 2890.1605993908997, (31, 18510): 2886.583639214547, (31, 18511): 2891.380738590739, (31, 18512): 2889.6472204851607, (31, 18515): 2891.9096490891243, (31, 18516): 2892.270628200859, (31, 18517): 2890.693177435037, (31, 18518): 2893.312977408315, (31, 18519): 2891.9151506643775, (31, 18520): 2889.5686396178244, (31, 18522): 2897.4715654186352, (31, 18523): 2897.852139818463, (31, 18532): 2899.849718298588, (31, 18535): 2895.788202462, (31, 18537): 2893.5267087658885, (31, 18539): 2894.044408434404, (31, 18540): 2894.354818871884, (31, 18541): 2895.506727363627, (31, 18542): 2896.2299112848027, (31, 18543): 2892.6716996509035, (31, 18546): 2894.505164420609, (31, 18555): 2898.057024420458, (31, 18556): 2898.759668044771, (31, 18565): 2899.7000112090773, (31, 18567): 2900.9002298345417, (31, 18568): 2898.894377029429, (31, 18577): 2912.7500511988305, (31, 18583): 2910.2002138305397, (31, 18605): 2912.8398444424624, (31, 18608): 2902.41466225961, (31, 18616): 2925.7942089990793, (31, 18618): 2936.9541434207044, (31, 18625): 2932.594327895364, (31, 18645): 2922.597420318221, (31, 18646): 2925.3420729225386, (31, 18653): 2916.7140487121, (31, 18654): 2925.608897274298, (31, 18655): 2919.8836897301567, (31, 18666): 2954.709749519254, (31, 18837): 2904.4779959477205, (31, 18974): 2879.933597703019, (31, 18999): 2888.0558387668857, (31, 19000): 2891.377578909671, (31, 19174): 2727.981011106519, (31, 19342): 2793.9372121152146, (31, 19455): 2756.4765286762477, (31, 19555): 2591.6336129413203, (31, 19564): 2601.2957328665607, (31, 19573): 2594.2389963186433, (31, 19586): 2591.09837348209, (31, 19605): 2593.776686516438, (31, 19611): 2598.5550795725703, (31, 19614): 2596.418893886869, (31, 19641): 2676.456332391229, (31, 19702): 2674.992623062873, (31, 19713): 2669.1517752371833, (31, 19731): 2564.52294282688, (31, 19819): 2731.165894730809, (31, 19893): 2525.197349228329, (31, 19899): 2557.0697209093482, (31, 19929): 2534.831391572805, (31, 19951): 2602.858655167624, (31, 19962): 2537.982706793426, (31, 19970): 2557.8307107239807, (31, 19971): 2557.019087320014, (31, 19972): 2550.451149619914, (31, 19975): 2548.5376789709994, (31, 19978): 2622.5824450056853, (31, 19987): 2624.55073272616, (31, 19989): 2605.6892666959393, (31, 20039): 2628.4064787858533, (31, 20043): 2637.393293361331, (31, 20047): 2632.3203585843244, (31, 20052): 2610.546686194452, (31, 20054): 2611.675299412132, (31, 20085): 2713.960739797737, (31, 20104): 2720.1556118864214, (31, 20132): 2681.121064092648, (31, 20203): 2510.6967668713905, (31, 20280): 2499.3242167932012, (31, 20285): 2495.82204367369, (31, 20290): 2503.3552031621184, (31, 20297): 2497.1949208265755, (31, 20309): 2618.9499295964406, (31, 20453): 2726.3567499935943, (31, 20485): 2458.0666519745237, (31, 20520): 2442.6092932089678, (31, 20526): 2432.714362801024, (31, 20698): 1684.1340516464516, (31, 20868): 1500.1512305631486, (31, 21042): 2321.5523713278017, (31, 21057): 2365.445474416261, (31, 21066): 2343.4340794678637, (31, 21075): 2335.90080579021, (31, 21093): 2324.162380119085, (31, 21098): 2354.3100485819864, (31, 21127): 2324.7954740135424, (31, 21130): 2332.735878567253, (31, 21144): 2332.1455420077714, (31, 21146): 2321.931289477033, (31, 21147): 2331.608304906268, (31, 21148): 2338.9926212138184, (31, 21153): 2323.3985376212827, (31, 21293): 2393.319091400503, (31, 21426): 2388.2075434256294, (31, 21442): 2435.7296145889486, (31, 21451): 2440.282566301306, (31, 21466): 2411.5580966655375, (31, 21469): 2418.330369444264, (31, 21471): 2408.1354924238694, (31, 21473): 2413.6672873715993, (31, 21475): 2408.645356559318, (31, 21482): 2422.8263937694383, (31, 21484): 2421.3015575956424, (31, 21488): 2417.3903221198702, (31, 21494): 2408.2971756028455, (31, 21498): 2413.4229841393017, (31, 21500): 2405.0671978135406, (31, 21514): 2417.682316983084, (31, 21537): 2402.9142586863027, (31, 21662): 2422.987156207489, (31, 21691): 2396.118079332449, (31, 21757): 2350.6695140845513, (31, 21777): 2234.6627646917036, (31, 21778): 2227.8840784958857, (31, 21779): 2231.292405221683, (31, 21790): 2242.702920682294, (31, 21802): 2241.6058677068427, (31, 21824): 2248.2761155433977, (31, 21874): 2232.586090859392, (31, 21879): 2227.8933251838607, (31, 21983): 2260.291057694286, (31, 22002): 2330.838700620438, (31, 22132): 2293.227431071574, (31, 22261): 1376.7633459834271, (31, 22298): 1393.957397833019, (31, 22339): 1331.032896147126, (31, 22508): 1503.6046142212679, (31, 22841): 983.3002603944411, (31, 22842): 979.8768961636938, (31, 22874): 964.3471704212603, (31, 22941): 976.4082557846008, (31, 22956): 975.730525289997, (31, 22960): 984.6558728063019, (31, 22968): 940.0043204897171, (31, 22970): 947.4541491815309, (31, 22974): 918.9888938336859, (31, 22980): 921.6899753898846, (31, 23025): 878.5791670156492, (31, 23028): 869.100541864362, (31, 23081): 820.5727533106323, (31, 23104): 741.6390735689654, (31, 23147): 846.815393506299, (31, 23298): 2533.820150843857, (31, 23376): 2514.270238987343, (31, 23381): 2501.326881930927, (31, 23529): 2545.2984612542705, (31, 23556): 2534.150778747275, (31, 23718): 2522.8043201807945, (31, 24001): 2649.6906911191563, (31, 24094): 2684.0510396462255, (31, 24129): 2703.4245571582715, (31, 24174): 2662.5104768848682, (31, 24235): 2705.11045191191, (31, 24259): 2724.0431698112598, (31, 24260): 2722.5920887689645, (31, 24261): 2718.4990604453383, (31, 24305): 2746.3011317566297, (31, 24306): 2749.9600322377105, (31, 24307): 2744.3697041752, (31, 24308): 2698.775574635009, (31, 24498): 2796.1376706116357, (31, 24499): 2796.5394516385386, (31, 24500): 2792.989676485463, (31, 24668): 2769.7344826219814, (31, 24711): 2819.908588444487, (31, 24756): 2832.744646153891, (31, 24788): 2838.310382393445, (31, 24809): 2816.787128935598, (31, 24813): 2823.5001576167638, (31, 24821): 2821.289456621246, (31, 24825): 2822.954319252806, (31, 24832): 2815.3073408127107, (31, 24833): 2818.6082761129346, (31, 24835): 2821.9047007451472, (31, 24837): 2827.134264068506, (31, 24840): 2814.8073189914303, (31, 24841): 2819.8842193498685, (31, 24844): 2814.9727885964026, (31, 24845): 2817.918639716792, (31, 24846): 2817.718430249085, (31, 24849): 2819.525019282787, (31, 24850): 2824.527988070248, (31, 24863): 2778.499750337662, (31, 24866): 2784.3955098929305, (31, 24885): 2791.445567432768, (31, 24886): 2791.99236906819, (31, 24889): 2804.775289336395, (31, 24903): 2809.698746611122, (31, 24909): 2788.0850025679106, (31, 24999): 3040.4844760727656, (31, 25019): 3033.2006843119116, (31, 25028): 3037.1709851817136, (31, 25137): 2498.2401216835683, (31, 25145): 2505.9017421510794, (31, 25208): 2581.358355401487, (31, 25233): 2570.596640715871, (31, 25371): 2506.8888900084826, (31, 25377): 2487.6391455755183, (31, 25828): 2106.9488338090478, (31, 25851): 2053.6790076686784, (31, 25874): 2107.18605613206, (31, 25898): 2127.6541571660623, (31, 25946): 2101.305850579067, (31, 26047): 2214.209981796408, (31, 26066): 2370.779524802225, (31, 26197): 2273.166243920727, (31, 26212): 1907.532602937778, (31, 26253): 1887.6737528868314, (31, 26254): 1895.2207544782923, (31, 26257): 1902.2352022113914, (31, 26258): 1891.6848630184227, (31, 26260): 1897.1038269222513, (31, 26266): 1889.3673538410287, (31, 26267): 1895.8090948178033, (31, 26271): 1896.0475349378323, (31, 26304): 1966.2306932362749, (31, 26305): 1965.621863453759, (31, 26363): 2083.068367533857, (31, 26441): 1451.2857387360839, (31, 26442): 1451.0258284509302, (31, 26450): 1460.437896795904, (31, 26459): 1469.9032011427216, (31, 26462): 1472.5128644317165, (31, 26467): 1446.8418742520216, (31, 26471): 1449.4752283233488, (31, 26472): 1448.9184489735371, (31, 26473): 1447.9409479564933, (31, 26476): 1439.1521721913928, (31, 26485): 1461.1234421287784, (31, 26493): 1456.3512468393803, (31, 26524): 1472.6304970360259, (31, 26525): 1471.1947197215814, (31, 26556): 1453.3906275140453, (31, 26560): 1461.73329506383, (31, 26561): 1469.0125912536987, (31, 26564): 1453.7427851163134, (31, 26569): 1467.886527546626, (31, 26570): 1467.254041698735, (31, 26573): 1461.8687887967733, (31, 26581): 1458.5605708247292, (31, 26583): 1462.6703587327474, (31, 26593): 1454.0806056504132, (31, 26837): 1441.4409366083285, (31, 26844): 1437.2829073317846, (31, 26863): 1437.7285973182609, (31, 26893): 1421.9268998307175, (31, 26902): 1415.9041487238528, (31, 26905): 1429.8593200101504, (31, 26912): 1422.6926436337753, (31, 26921): 1430.6791439831225, (31, 26922): 1431.0071723099725, (31, 27212): 1615.3787720371238, (31, 27218): 1629.1850112637865, (31, 27239): 1606.525423023168, (31, 27257): 1606.7100264864134, (31, 27274): 1603.2353842077175, (31, 27279): 1600.2675603683933, (31, 27282): 1604.5268819859502, (31, 27283): 1610.0334449477307, (31, 27285): 1599.0984100450562, (31, 27286): 1596.5200856410281, (31, 27290): 1607.5864196358923, (31, 27295): 1615.708416975455, (31, 27300): 1603.9777292938063, (31, 27344): 1598.8326645842294, (31, 27366): 1590.3220226264455, (31, 27383): 1590.9405361272347, (31, 27398): 1594.8946735119835, (31, 27406): 1601.7779241275844, (31, 27407): 1603.541014567964, (31, 27426): 1634.3505472982001, (31, 27432): 1644.4760958106199, (31, 27460): 1641.4650229292229, (31, 27523): 1532.6202176899324, (31, 27545): 1524.2986589913019, (31, 27602): 1412.4679414408045, (31, 27606): 1416.2912575661853, (31, 27646): 1435.5577374682587, (31, 27667): 1412.4945396025635, (31, 27672): 1414.2350709051784, (31, 27674): 1416.301455263573, (31, 27688): 1424.646197230607, (31, 27692): 1406.9321313836447, (31, 27693): 1409.7304049822703, (31, 27705): 1406.575422892581, (31, 27712): 1402.3747370895, (31, 27786): 1542.322704711822, (31, 27790): 1596.2915597352094, (31, 27791): 1603.6090853506253, (31, 27795): 1542.2662377250388, (31, 27801): 1578.2266543704052, (31, 27813): 1534.8600914582812, (31, 27816): 1546.6538261586247, (31, 27823): 1579.9999054474877, (31, 27830): 1560.3721550257767, (31, 27884): 1443.2202800822163, (31, 27885): 1440.3327978321597, (31, 27896): 1443.4174982273857, (31, 27919): 1446.6545704703449, (31, 27922): 1441.780833358281, (31, 27930): 1446.455911968607, (31, 27934): 1443.6335866192535, (31, 27935): 1440.4626007208235, (31, 27948): 1258.885401155922, (31, 27951): 1305.5333239151983, (31, 28061): 1100.6014704899612, (31, 28290): 835.7958137164571, (31, 28292): 818.9702864542735, (31, 28293): 831.5609987621483, (31, 28295): 826.175138574859, (31, 28296): 832.0041627288966, (31, 28297): 843.9269271852514, (31, 28302): 838.8444508258076, (31, 28310): 696.0196523253562, (31, 28313): 706.8956561481498, (31, 28372): 676.9260198268564, (31, 28398): 678.577364353256, (31, 28399): 682.3590149073732, (31, 28400): 679.9664290929994, (31, 28401): 682.7538698958824, (31, 28445): 718.7021608920976, (31, 28475): 668.8267887786732, (31, 28885): 2697.1397216017745, (31, 28886): 2693.061479567112, (31, 28915): 2694.552667077663, (31, 28916): 2691.989170034246, (31, 28917): 2689.6375440284055, (31, 28921): 2704.3211551462477, (31, 28931): 2702.8895076568447, (31, 28945): 2679.0117416358926, (31, 28982): 2685.373358018992, (31, 29219): 2696.6617836390146, (31, 29228): 2680.734089874238, (31, 29246): 2779.0364783265954, (31, 29248): 2775.6542691782333, (31, 29282): 2754.8512644255106, (31, 29290): 2791.437493947084, (31, 29291): 2786.6467075470314, (31, 29292): 2790.8591884720404, (31, 29293): 2782.6216349574825, (31, 29294): 2788.362481987418, (31, 29298): 2782.7402895193063, (31, 29299): 2781.520849571891, (31, 29304): 2774.957147086385, (31, 29317): 2755.8472115264885, (31, 29323): 2754.4198940905094, (31, 29330): 2763.540665118413, (31, 29331): 2768.494122153596, (31, 29344): 2694.666390723856, (31, 29445): 2503.6664942386255, (31, 29724): 1114.7879726271387, (31, 29738): 1115.1686044941723, (31, 29745): 1119.2305137019728, (31, 29748): 1145.522040903994, (31, 29750): 1157.1233791803825, (31, 29759): 1141.8101541801511, (31, 29772): 1143.6550470688383, (31, 29781): 1143.9917330467756, (31, 29784): 1132.48934575131, (31, 29790): 1148.9902243557424, (31, 29811): 1159.461645026063, (31, 29817): 1230.7184884558274, (31, 29818): 1231.4291098804495, (31, 29929): 1102.8097857048965, (31, 30039): 1035.141275823743, (31, 30066): 989.2790754183346, (31, 30116): 1037.948766922646, (31, 30238): 1119.0168687576934, (31, 30248): 1004.5312400435666, (31, 30260): 997.1665224632535, (31, 30545): 2646.23198462338, (31, 30733): 2474.2311996334147, (31, 30756): 2422.1105828129516, (31, 30921): 2508.763145907188, (31, 31079): 2078.578652707906, (31, 31149): 2055.470724394649, (31, 31154): 2055.8596187686494, (31, 31160): 2054.1239003147475, (31, 31163): 2053.0847331820796, (31, 31189): 1980.1628075038675, (31, 31215): 1984.370599008977, (31, 31259): 1974.877914658431, (31, 31262): 1967.0291934521392, (31, 31430): 2085.7823859471437, (31, 31568): 1880.2805794818173, (31, 31751): 2038.7654442196583, (32, 109): 245.93929131899804, (32, 872): 1488.3068533357139, (32, 873): 1496.8157786036086, (32, 877): 1494.5504272451847, (32, 879): 1495.9030357884312, (32, 884): 1489.4418729872218, (32, 889): 1494.3293091077655, (32, 891): 1486.375557740706, (32, 892): 1502.3067589351342, (32, 894): 1500.8529135591375, (32, 896): 1491.1203648644694, (32, 903): 1495.9325056316784, (32, 909): 1478.4047999930926, (32, 910): 1480.9583321330624, (32, 912): 1475.5320698265623, (32, 913): 1469.8677678511813, (32, 916): 1466.2236009883256, (32, 926): 1482.6320914161581, (32, 927): 1479.5863865691963, (32, 948): 1483.140980878002, (32, 961): 1484.3183574230836, (32, 962): 1484.6884002238266, (32, 963): 1485.2974494905313, (32, 967): 1499.1513841531864, (32, 974): 1496.7688055197327, (32, 998): 1503.2846541375975, (32, 1014): 1678.2460360597781, (32, 1086): 1443.542021847285, (32, 1087): 1439.6824492828835, (32, 1089): 1433.3182941702116, (32, 1090): 1437.1207885038411, (32, 1092): 1449.346379391655, (32, 1097): 1440.573738529023, (32, 1107): 1453.6715061265834, (32, 1387): 163.1938403753572, (32, 1554): 81.96767781413408, (32, 1827): 1896.32974234181, (32, 1828): 1896.8115405276828, (32, 1829): 1898.4049694223418, (32, 1830): 1899.0451760575631, (32, 1831): 1899.4538417785357, (32, 1832): 1898.3447334796983, (32, 1833): 1898.1060285767785, (32, 1836): 1896.7401825586533, (32, 1841): 1902.6989533281835, (32, 1843): 1900.4124750751546, (32, 1844): 1901.7692353893538, (32, 1845): 1899.3449963516628, (32, 1847): 1889.5307066939624, (32, 1848): 1892.688328950556, (32, 1849): 1907.8245945742465, (32, 1850): 1909.0590082261085, (32, 1851): 1896.0133985299176, (32, 1852): 1897.0317645106975, (32, 1854): 1897.919289925729, (32, 1856): 1890.1255290472095, (32, 1857): 1892.9029900183532, (32, 1858): 1905.8401649522157, (32, 1861): 1898.883622626667, (32, 1866): 1890.6077359806573, (32, 1867): 1902.1925878190793, (32, 1868): 1899.7141855429431, (32, 1870): 1902.5342628637352, (32, 1871): 1901.1162517977832, (32, 1875): 1897.2271317889913, (32, 1880): 1891.3845160019525, (32, 1882): 1893.4369141981713, (32, 1883): 1908.2842654777635, (32, 1889): 1891.697537293226, (32, 1893): 1897.2906819194723, (32, 1894): 1894.898654384677, (32, 1899): 1889.246805606721, (32, 1900): 1890.5768472453126, (32, 1902): 1901.0530890369002, (32, 1905): 1904.3630543661488, (32, 1907): 1893.9841101770862, (32, 1910): 1894.0446167661464, (32, 1917): 1907.6946360090794, (32, 1920): 1893.5009782151, (32, 1935): 1903.2387252380845, (32, 1937): 1905.878057404077, (32, 1946): 1882.6568349098875, (32, 1949): 1884.8964723965464, (32, 1950): 1877.6132264353346, (32, 1951): 1881.559676947676, (32, 1952): 1886.9421039246904, (32, 1953): 1886.5083347711102, (32, 1954): 1885.785040086096, (32, 1958): 1884.994717564984, (32, 1960): 1889.9748012202451, (32, 1968): 1891.935444587689, (32, 1969): 1902.2644121756634, (32, 1974): 1899.6988212682309, (32, 1975): 1900.1757842029965, (32, 1979): 1892.8831651160897, (32, 1980): 1893.9242698420683, (32, 1981): 1894.7936304997272, (32, 1985): 1895.8790999873024, (32, 1994): 1877.6037844985772, (32, 2011): 1893.855258280359, (32, 2019): 1918.0733149038517, (32, 2020): 1914.8825357691546, (32, 2029): 1904.289310743872, (32, 2030): 1912.6464320301122, (32, 2032): 1903.3466680365239, (32, 2033): 1908.2018809933174, (32, 2034): 1908.8734080941886, (32, 2036): 1901.2363691362227, (32, 2037): 1903.0637147065436, (32, 2038): 1900.3738664802902, (32, 2042): 1934.6975722491543, (32, 2050): 1905.5370809188187, (32, 2051): 1905.8714212980583, (32, 2053): 1906.4179336719505, (32, 2054): 1909.4829626931437, (32, 2066): 1903.3916382077282, (32, 2067): 1902.9866457695493, (32, 2071): 1871.4766837242828, (32, 2072): 1876.5034527989965, (32, 2073): 1858.9166046809685, (32, 2074): 1858.677380292335, (32, 2080): 1850.4937508923615, (32, 2082): 1879.4000241117662, (32, 2083): 1881.949974577098, (32, 2089): 1875.2168136464913, (32, 2090): 1877.4559058374264, (32, 2092): 1873.3153148991153, (32, 2098): 1853.059884523802, (32, 2099): 1856.8087760060723, (32, 2101): 1853.1980456391702, (32, 2102): 1867.4935241742687, (32, 2103): 1863.2945847074675, (32, 2104): 1861.3438715212392, (32, 2106): 1884.2235189154044, (32, 2112): 1855.7797500736315, (32, 2113): 1869.9776594153989, (32, 2114): 1874.6889329297044, (32, 2117): 1887.0210022665663, (32, 2123): 1837.553883746255, (32, 2124): 1840.5120360838691, (32, 2134): 1833.9310880127637, (32, 2138): 1841.8929623065271, (32, 2141): 1834.386367241829, (32, 2148): 1845.948795989937, (32, 2150): 1827.5325359670803, (32, 2151): 1831.1724925275141, (32, 2152): 1826.3877889598955, (32, 2153): 1846.2506863902743, (32, 2154): 1833.5489854608272, (32, 2155): 1833.3758788671691, (32, 2156): 1830.2125192144692, (32, 2157): 1837.8533653185114, (32, 2160): 1849.4911077497434, (32, 2161): 1826.593365452224, (32, 2162): 1849.5404335656453, (32, 2163): 1845.1428499916665, (32, 2164): 1845.311692049489, (32, 2168): 1832.4359334787157, (32, 2172): 1838.5414078041897, (32, 2174): 1831.7217393994108, (32, 2178): 1841.9528254051374, (32, 2179): 1840.3197744167414, (32, 2183): 1842.5204145462556, (32, 2185): 1843.1508537924233, (32, 2186): 1840.5541983410449, (32, 2190): 1849.2817866873522, (32, 2192): 1844.759605839443, (32, 2193): 1843.1016071478307, (32, 2194): 1838.4856647653305, (32, 2195): 1838.7708111671648, (32, 2197): 1846.2177743927216, (32, 2205): 1841.1144083889078, (32, 2207): 1834.1779553514311, (32, 2208): 1838.2487545794227, (32, 2212): 1842.3704749256374, (32, 2214): 1766.6584596190628, (32, 2225): 1780.2653687869658, (32, 2231): 1738.3298889948715, (32, 2278): 1831.612177668017, (32, 2284): 1842.549040759524, (32, 2285): 1841.9125067492112, (32, 2291): 1827.889525923473, (32, 2292): 1824.5446893845683, (32, 2307): 1836.6301262221039, (32, 2313): 1827.3904940962327, (32, 2317): 1815.5176194836226, (32, 2319): 1828.2741672131604, (32, 2321): 1833.4330548510407, (32, 2323): 1831.370380683504, (32, 2326): 1844.9080126166386, (32, 2327): 1840.8628737731835, (32, 2329): 1838.2550355143853, (32, 2330): 1835.6348817817916, (32, 2332): 1842.996010883007, (32, 2344): 1830.5455694104887, (32, 2346): 1831.392476662631, (32, 2361): 1821.2494174893295, (32, 2368): 1873.3629299979225, (32, 2374): 1878.6120116723828, (32, 2375): 1879.5929745067094, (32, 2377): 1863.246687622291, (32, 2378): 1882.8451139865444, (32, 2379): 1884.2693265853075, (32, 2380): 1885.0812186979188, (32, 2383): 1866.7886350256854, (32, 2385): 1868.8434321550249, (32, 2395): 1868.2042980185943, (32, 2397): 1882.876497486756, (32, 2398): 1858.1526948187357, (32, 2399): 1863.316803147939, (32, 2400): 1862.0308711414084, (32, 2402): 1873.858582398454, (32, 2403): 1877.4372409937414, (32, 2404): 1877.9374972369844, (32, 2405): 1869.6924270899056, (32, 2407): 1875.7986166612288, (32, 2408): 1880.4343757408624, (32, 2409): 1872.0325610984964, (32, 2411): 1879.1255102174246, (32, 2412): 1877.5429764327441, (32, 2413): 1880.713964984475, (32, 2414): 1876.1750504707334, (32, 2422): 1878.6356486004, (32, 2424): 1878.176874929719, (32, 2426): 1878.6034254232213, (32, 2433): 1872.6192356588992, (32, 2436): 1871.9741625170614, (32, 2437): 1850.834960331768, (32, 2440): 1855.1870740703157, (32, 2445): 1956.5109782181257, (32, 2447): 1944.2235757962908, (32, 2454): 1954.8317983231043, (32, 2455): 1954.5948455187704, (32, 2460): 1922.7574325239345, (32, 2461): 1926.8679520105356, (32, 2471): 1997.0959655800893, (32, 2492): 1961.0781330159527, (32, 2511): 1922.7453797273777, (32, 2523): 1942.4707225401692, (32, 2525): 1939.4136824475945, (32, 2535): 1930.0479151859483, (32, 2537): 1923.3934972140623, (32, 2538): 1927.1438525245767, (32, 2539): 1929.2126592859966, (32, 2540): 1933.173039092243, (32, 2542): 1939.443465051317, (32, 2559): 2031.7839162746257, (32, 2575): 2027.5122238653444, (32, 2599): 1863.4454088007085, (32, 2600): 1900.3355357784944, (32, 2607): 1875.912858969082, (32, 2627): 1957.9696709625675, (32, 2647): 1979.8607616594982, (32, 2674): 1965.4338751200273, (32, 2681): 1965.0763878961648, (32, 2683): 1973.2913778917004, (32, 2686): 1961.5773138199988, (32, 2689): 2086.9843311275217, (32, 2690): 2088.129930281359, (32, 2713): 2128.5351252150476, (32, 2714): 2132.895633214231, (32, 2715): 2135.8129489142566, (32, 2739): 2132.550363606198, (32, 2740): 2107.7739973291964, (32, 2741): 2108.7790515777797, (32, 2749): 2130.932887747327, (32, 2750): 2131.032010067243, (32, 2752): 2132.7451137973208, (32, 2755): 2135.5707252038897, (32, 2758): 2135.581106308181, (32, 2759): 2135.2248603327143, (32, 2769): 2130.899087877088, (32, 2771): 2114.150088249272, (32, 2779): 2120.9808572522265, (32, 2784): 2090.4929612853143, (32, 2800): 2102.331538254621, (32, 2802): 2105.237473300805, (32, 2803): 2103.378169906006, (32, 2804): 2101.1186767887625, (32, 2805): 2109.9560361474637, (32, 2807): 2109.020232659039, (32, 2809): 2109.6042268438023, (32, 2812): 2088.799188370673, (32, 2814): 2113.6108792635036, (32, 2817): 2121.0652399553283, (32, 2819): 2107.5669174970676, (32, 2823): 2097.167188372692, (32, 2832): 2114.6811702442274, (32, 2836): 2101.3042237498707, (32, 2839): 2108.215812908039, (32, 2841): 2118.265386439044, (32, 2843): 2116.0582864281805, (32, 2846): 2106.9890112788476, (32, 2849): 2118.038262477066, (32, 2852): 2114.5189446279946, (32, 2853): 2119.704593361338, (32, 2876): 2124.573456194149, (32, 2877): 2135.8187699588166, (32, 2885): 2146.260760741609, (32, 2918): 2104.3021161519587, (32, 2921): 2109.8218278295017, (32, 2925): 2081.5164007993767, (32, 2926): 2070.6998459170086, (32, 2930): 2098.97205335419, (32, 2931): 2085.5685976432064, (32, 2938): 2105.65949100788, (32, 2940): 2113.036085222891, (32, 2947): 2095.561134175023, (32, 2949): 2095.8907578523745, (32, 2950): 2099.2552102008704, (32, 2952): 2097.000800848705, (32, 2958): 2096.026933407101, (32, 2959): 2096.7570389149287, (32, 2960): 2102.358892471396, (32, 2961): 2100.4920717304003, (32, 2963): 2094.8269947529197, (32, 2968): 2097.0476579958818, (32, 2976): 2093.4397109136003, (32, 2981): 2059.338596439349, (32, 2982): 2059.6527782353824, (32, 2984): 2057.7703630037868, (32, 3003): 2055.563860336724, (32, 3046): 2008.5061021589256, (32, 3050): 2039.9342810097855, (32, 3051): 2041.1193809141012, (32, 3053): 2036.8204618104203, (32, 3069): 2067.0410471637747, (32, 3071): 2032.0956154877392, (32, 3080): 2148.9397949020654, (32, 3199): 2057.8985134012873, (32, 3200): 2053.810182483858, (32, 3205): 2084.7237636219656, (32, 3209): 2056.686796640142, (32, 3215): 2053.248670658485, (32, 3217): 2047.139047919111, (32, 3249): 2052.879338050359, (32, 3263): 2098.673767456511, (32, 3289): 2064.9821196404573, (32, 3301): 2068.728864541657, (32, 3302): 2065.685460633182, (32, 3307): 2062.697827478592, (32, 3310): 2071.3638615148893, (32, 3391): 2121.712884624096, (32, 3509): 1038.091014628339, (32, 3510): 1033.810472893906, (32, 3511): 1035.1527081009613, (32, 3512): 1031.1832654062268, (32, 3514): 1030.8911840547644, (32, 3519): 1055.5167512246642, (32, 3536): 1043.0068091474707, (32, 3545): 1048.235362756583, (32, 3548): 1039.6954532135035, (32, 3572): 1047.263600063201, (32, 3581): 1047.0954667266997, (32, 3583): 1037.976014478703, (32, 3601): 1065.8920372744797, (32, 3656): 1064.7807972719845, (32, 3669): 1069.214399687836, (32, 3670): 1073.5615552451004, (32, 3695): 1046.471006573214, (32, 3696): 1049.2451126550156, (32, 3782): 1015.8431242691219, (32, 3792): 1014.8986290980083, (32, 3989): 1210.8061680794983, (32, 4008): 1236.7326708932305, (32, 4031): 1240.5879137322715, (32, 4045): 1226.1098265017317, (32, 4144): 1222.3438829905133, (32, 4145): 1190.683207555087, (32, 4164): 1210.999446840865, (32, 4168): 1200.282234844815, (32, 4173): 1197.3224507528264, (32, 4181): 1181.5190039966797, (32, 4228): 1172.5410071101453, (32, 4248): 1157.996161433875, (32, 4254): 990.4341231260697, (32, 4260): 993.6868318966688, (32, 4262): 1001.1487848636715, (32, 4273): 1000.8848837234383, (32, 4319): 898.5157141567037, (32, 4326): 896.2213277742683, (32, 4328): 898.1679770507566, (32, 4334): 901.5023038128985, (32, 4335): 898.8394972675194, (32, 4372): 686.3216685484099, (32, 4413): 766.4012841461913, (32, 4434): 682.7486604230619, (32, 4447): 692.4318719438135, (32, 4452): 683.9763619242561, (32, 4463): 533.8491290068678, (32, 4465): 538.20146659932, (32, 4619): 780.4894653474049, (32, 4645): 796.4102731194425, (32, 4657): 794.4373577595776, (32, 4666): 788.5594808344418, (32, 4676): 800.2575655377153, (32, 4678): 802.5370797508483, (32, 4689): 795.4190268868985, (32, 4704): 853.6766613851919, (32, 4726): 1009.7276845885602, (32, 4727): 1006.8871764233031, (32, 4730): 1001.326183025869, (32, 4731): 1003.2795964526161, (32, 4734): 1004.4037430780293, (32, 4735): 1002.00815678438, (32, 4736): 1003.6122433632783, (32, 4737): 999.1944151147211, (32, 4738): 1000.0374531603601, (32, 4756): 1003.0323523800892, (32, 4760): 987.4436011325114, (32, 4761): 988.524142659362, (32, 4762): 983.901515877212, (32, 4765): 988.9918331964296, (32, 4773): 1015.0212014009754, (32, 4774): 1012.9213405057995, (32, 4790): 1013.0702809427287, (32, 4795): 1010.4849833591691, (32, 4799): 1014.38481423113, (32, 4801): 1020.970494503846, (32, 4804): 1010.9296411730897, (32, 4805): 1008.8185558570489, (32, 4806): 1012.4998290935564, (32, 4815): 1010.1740056393896, (32, 4816): 1017.0986230920265, (32, 4817): 1019.051077241741, (32, 4826): 1014.6309936006217, (32, 4830): 1010.8125752678263, (32, 4839): 995.6904605358908, (32, 4840): 998.4035502119368, (32, 4841): 992.6048688649755, (32, 4846): 990.5706678831137, (32, 4848): 990.3180880944924, (32, 4850): 992.9561116783536, (32, 4871): 958.6507189440832, (32, 4883): 983.7402757824055, (32, 4900): 970.3638112645814, (32, 4901): 967.127280218389, (32, 4917): 785.7672111186739, (32, 4931): 765.5360510886791, (32, 4944): 787.7355681094103, (32, 4956): 769.572864134625, (32, 4958): 769.6582982349388, (32, 4959): 766.2920472122827, (32, 4961): 773.4044858009945, (32, 4966): 765.0114594104514, (32, 5207): 742.6584379669532, (32, 5272): 385.33158787099416, (32, 5283): 390.7502463228888, (32, 5287): 395.39694598612715, (32, 5289): 397.7951162327576, (32, 5293): 391.2208073822043, (32, 5295): 406.8305615048704, (32, 5296): 403.90396294270084, (32, 5298): 402.1998788407156, (32, 5303): 404.8706821691469, (32, 5305): 376.49284440524764, (32, 5306): 368.1700359962396, (32, 5307): 373.278653712502, (32, 5308): 378.27357320115084, (32, 5313): 381.4976477421502, (32, 5314): 386.1599234338502, (32, 5317): 376.60826291091325, (32, 5319): 398.5370350271813, (32, 5324): 397.22598246176915, (32, 5326): 396.6461976473312, (32, 5348): 364.59036607888186, (32, 5351): 365.72132818022806, (32, 5399): 397.945550968667, (32, 5413): 369.31289891429964, (32, 5422): 403.440915638882, (32, 5445): 388.4847657071987, (32, 5448): 382.7120746132331, (32, 5456): 378.8168191642255, (32, 5467): 383.63004844171115, (32, 5624): 334.73753838526414, (32, 5671): 548.638326895182, (32, 5672): 541.2975279950431, (32, 5797): 644.3049785596526, (32, 5871): 479.8912708906173, (32, 5976): 399.29693522850886, (32, 6118): 1668.7154884028753, (32, 6248): 1798.4701193644012, (32, 6345): 589.7206563957895, (32, 6352): 595.1972786392331, (32, 6354): 585.9930582266285, (32, 6359): 589.5109195939705, (32, 6376): 605.2718765551073, (32, 6378): 587.0879192947855, (32, 6381): 593.0095252471849, (32, 6383): 589.0213380475648, (32, 6396): 611.2775961411031, (32, 6399): 595.0604966041017, (32, 6408): 590.4771609481195, (32, 6409): 575.9499628918568, (32, 6419): 566.8381808310552, (32, 6422): 580.3515958416864, (32, 6423): 580.1452426770716, (32, 6424): 573.1616091749243, (32, 6439): 570.2684248767401, (32, 6464): 567.9433827767283, (32, 6465): 572.5408114625079, (32, 6469): 580.5212148613344, (32, 6470): 582.8302614880869, (32, 6472): 589.7000113957043, (32, 6480): 571.0007372262002, (32, 6486): 547.8062162424884, (32, 6497): 554.5278104192582, (32, 6503): 543.668680778095, (32, 6508): 556.2845174695974, (32, 6509): 549.4814377569903, (32, 6521): 561.645686559773, (32, 6544): 549.5962535355324, (32, 6552): 558.2010209461856, (32, 6553): 557.7147544816662, (32, 6554): 557.4060012678405, (32, 6578): 560.8646584117529, (32, 6582): 547.7775999720673, (32, 6601): 558.3328117191469, (32, 6609): 573.7434372734151, (32, 6610): 571.105875019063, (32, 6611): 578.1591659755182, (32, 6614): 582.2237047230323, (32, 6615): 579.8232600141015, (32, 6616): 570.9627730199124, (32, 6617): 574.0604614352395, (32, 6618): 565.1995336570337, (32, 6619): 580.6729361682358, (32, 6620): 566.6120216262751, (32, 6621): 565.5306532551923, (32, 6622): 568.5941187468665, (32, 6623): 577.4603789009296, (32, 6624): 572.7573952841406, (32, 6625): 575.0792056943872, (32, 6626): 582.5649686712054, (32, 6627): 585.983456100231, (32, 6628): 562.1289683355258, (32, 6629): 567.4446168475288, (32, 6630): 581.9411668336759, (32, 6632): 569.8513552701125, (32, 6634): 579.0164862444057, (32, 6635): 567.8239305267884, (32, 6636): 569.4652335156154, (32, 6637): 566.749557130415, (32, 6638): 577.8116614196595, (32, 6639): 583.4634572522816, (32, 6640): 580.0375032363983, (32, 6641): 562.1081577294332, (32, 6642): 574.912102789472, (32, 6643): 585.6459818213124, (32, 6645): 578.7154276965541, (32, 6646): 568.5535610025013, (32, 6647): 576.5662494408217, (32, 6653): 581.155315299911, (32, 6655): 584.8769782351783, (32, 6658): 577.3034652770036, (32, 6662): 571.7844661052654, (32, 6819): 527.3598637921868, (32, 6996): 450.7634114965132, (32, 7059): 450.37788333434315, (32, 7187): 303.88538269694607, (32, 7304): 409.7967573837282, (32, 7528): 386.42355602721614, (32, 7720): 480.2729517532756, (32, 7793): 456.7325823639821, (32, 7807): 465.06344453527583, (32, 7808): 451.28283078094114, (32, 7831): 545.7869882213375, (32, 7850): 573.7602292347058, (32, 7852): 578.0419639274339, (32, 8012): 506.96666067969363, (32, 8125): 378.3405678963535, (32, 8208): 509.11608959300145, (32, 8392): 484.232825872509, (32, 8651): 582.6599676961392, (32, 9088): 614.8596228306451, (32, 9443): 448.9458146598192, (32, 9444): 442.406759253653, (32, 9828): 537.6852508024307, (32, 9868): 587.8455477378452, (32, 10180): 371.97345201572836, (32, 10256): 431.1310730411844, (32, 10276): 415.67886338104324, (32, 10378): 470.9634232029644, (32, 10676): 280.2989916550449, (32, 10714): 220.32386359554576, (32, 10730): 285.5485730797291, (32, 10862): 410.9232719325934, (32, 10881): 419.0702369348135, (32, 10883): 420.149943875164, (32, 10885): 408.7099614093071, (32, 10891): 421.9270838480799, (32, 10909): 416.418591952838, (32, 10911): 412.6729974353641, (32, 10913): 412.34654904500553, (32, 10915): 409.7282161219032, (32, 10919): 408.7625946805548, (32, 11037): 429.771263947571, (32, 11039): 395.16617513656274, (32, 11516): 1536.4983088778354, (32, 11856): 903.6436647671931, (32, 11857): 895.7492059040771, (32, 11861): 899.7156944937072, (32, 11881): 901.8012637879198, (32, 11902): 886.4390994640399, (32, 11911): 888.3012958289905, (32, 11914): 888.395539081039, (32, 11922): 898.189620847139, (32, 11924): 902.986486973453, (32, 11926): 898.8350132149928, (32, 11950): 912.6041181448497, (32, 11963): 926.3283014121916, (32, 11983): 924.8338050085906, (32, 11985): 932.8308971445448, (32, 12009): 936.9142366444495, (32, 12010): 925.4675704821838, (32, 12018): 928.0110926507197, (32, 12020): 929.6666449267623, (32, 12021): 932.0462859638765, (32, 12024): 941.4240341811645, (32, 12025): 936.8522452443632, (32, 12027): 934.975048348889, (32, 12031): 923.7915829594672, (32, 12032): 925.9527888361752, (32, 12035): 937.8808942836454, (32, 12041): 930.0731820005807, (32, 12045): 808.8066030755444, (32, 12145): 874.8839352465598, (32, 12275): 1233.7665478141844, (32, 12294): 1217.338842281975, (32, 12358): 1302.2849821384068, (32, 12463): 1340.7486440725702, (32, 12465): 1340.343819030749, (32, 12482): 1346.2183087776484, (32, 12503): 1346.2006659390313, (32, 12506): 1349.597980127835, (32, 12549): 1333.6701327136534, (32, 12559): 1332.7832465656281, (32, 12569): 1338.609604133024, (32, 12572): 1340.989376046408, (32, 12574): 1335.0702914805343, (32, 12576): 1335.598462572559, (32, 12591): 1330.0989937465529, (32, 12608): 1347.1947878948326, (32, 12696): 1310.9352334951789, (32, 12710): 1323.8761789428913, (32, 12728): 1321.2814631883627, (32, 12766): 801.2771087646606, (32, 12771): 753.020170160651, (32, 12790): 751.2303827507578, (32, 12795): 750.6862080493064, (32, 12797): 706.3444574106115, (32, 12798): 708.9514689794811, (32, 12811): 732.7027826857355, (32, 12830): 729.9840726684765, (32, 12848): 723.4116487592499, (32, 12850): 719.0244610211715, (32, 12852): 725.6469328659606, (32, 12854): 722.1112016594403, (32, 12859): 724.1963670247413, (32, 12861): 710.4024211187257, (32, 12865): 741.796130960102, (32, 12866): 736.8159430655878, (32, 12867): 746.8429161267334, (32, 12874): 742.4121403410678, (32, 12875): 743.805387768283, (32, 12881): 736.2765351889507, (32, 12883): 740.3192736158494, (32, 12885): 746.8898985542328, (32, 12888): 736.2019929830699, (32, 12889): 733.1536748928731, (32, 12892): 744.3851601818449, (32, 12893): 738.5229717244808, (32, 12896): 738.4574602902245, (32, 12906): 752.2131762205065, (32, 13018): 780.6592254540207, (32, 13071): 794.2860777198193, (32, 13131): 717.0986969042435, (32, 13146): 726.0809008394973, (32, 13159): 769.3469597848726, (32, 13193): 709.3727606558151, (32, 13198): 653.8934183298045, (32, 13292): 685.3605001255999, (32, 13296): 673.5401692594046, (32, 13406): 675.830039741477, (32, 13407): 678.2035619850692, (32, 13417): 702.0537784646068, (32, 13418): 708.982691451434, (32, 13438): 700.4392899142166, (32, 13442): 694.3875429989281, (32, 13443): 693.1566061688486, (32, 13764): 832.8706199168066, (32, 13766): 831.4209621651937, (32, 13771): 843.0180973304391, (32, 13783): 817.086129383247, (32, 13784): 825.4767673680161, (32, 13792): 861.1690445968379, (32, 13824): 820.1762296074514, (32, 14017): 752.0424943767987, (32, 14870): 311.4685927351281, (32, 14997): 297.1366824458605, (32, 15000): 291.23404391121585, (32, 15003): 284.60036390998204, (32, 15006): 308.4986807068779, (32, 15007): 307.22761804468865, (32, 15056): 289.890555379932, (32, 15063): 287.07875981599227, (32, 15069): 280.71045434194593, (32, 15076): 303.005510766014, (32, 15086): 312.71520679771663, (32, 15087): 305.49437301824753, (32, 15111): 314.14100718537054, (32, 15116): 308.52955640965496, (32, 15722): 354.86378468839774, (32, 15998): 282.2050746469015, (32, 16073): 1444.7615843760143, (32, 16939): 1662.6906949084446, (32, 16940): 1656.286724953201, (32, 16951): 1666.6472167590066, (32, 16963): 1666.5023303996875, (32, 16965): 1672.9445703410784, (32, 16969): 1672.984328190311, (32, 16970): 1668.2372450698274, (32, 16971): 1662.32091325336, (32, 16973): 1663.0342417253635, (32, 16974): 1676.5945220688563, (32, 16976): 1667.9966223331562, (32, 16978): 1663.2850619741498, (32, 16980): 1669.2468683925995, (32, 16982): 1677.7041089681056, (32, 17045): 1958.7914714908816, (32, 17048): 1967.0800252589117, (32, 17304): 1113.7365429751555, (32, 17305): 1113.8006092528756, (32, 17330): 1116.3423625681387, (32, 17334): 1105.1558321411046, (32, 17343): 1123.0447460072744, (32, 17345): 1109.161453648807, (32, 17347): 1118.598724810877, (32, 17351): 1094.4992756616716, (32, 17372): 1105.9018824429852, (32, 17373): 1121.930937291093, (32, 17377): 1123.4064216540532, (32, 17382): 1113.8759712622636, (32, 17383): 1114.2117878202555, (32, 17389): 1108.933017960186, (32, 17400): 1117.9354841620154, (32, 17401): 1117.0685119970444, (32, 17402): 1118.9112535431743, (32, 17403): 1120.2080624793136, (32, 17440): 1114.4229362748424, (32, 17455): 1124.2067319147893, (32, 17491): 1128.2976705757599, (32, 17507): 1089.623099841566, (32, 17509): 1093.712646998421, (32, 17590): 1095.876369096004, (32, 17615): 1040.0031496608358, (32, 17642): 1047.2697311399895, (32, 17643): 1048.424883989792, (32, 17668): 1038.7930395193096, (32, 17721): 1017.6907666019647, (32, 17754): 1064.04290276449, (32, 17769): 1086.5643817141274, (32, 17776): 1073.789847838173, (32, 17804): 1094.186033724529, (32, 17809): 1099.3372513153404, (32, 17824): 1093.3712645994688, (32, 17837): 1090.8265352291294, (32, 17838): 1093.7787315393618, (32, 17862): 1091.122933990442, (32, 17866): 1100.8719480783834, (32, 17872): 1085.9920547810152, (32, 17873): 1079.1031800607357, (32, 17881): 1090.0384122129665, (32, 17947): 1116.6886150719138, (32, 17951): 1107.3883677008737, (32, 17953): 1104.4508707965813, (32, 17954): 1104.3417103612503, (32, 17959): 1116.765090507013, (32, 17963): 1115.5274804232251, (32, 18000): 1065.399792912829, (32, 18001): 1065.6091901378, (32, 18111): 1163.4479898861866, (32, 18148): 892.4111930548543, (32, 18166): 991.0293391118435, (32, 18189): 1094.9111064444066, (32, 18239): 1122.9239997300606, (32, 18240): 1123.3128168143826, (32, 18245): 1123.6370219331923, (32, 18247): 1122.9925146525757, (32, 18251): 1124.1655237333102, (32, 18256): 1125.9618126831847, (32, 18258): 1124.9332598251726, (32, 18259): 1125.4083713603782, (32, 18260): 1126.2486411269472, (32, 18262): 1127.5138646888456, (32, 18263): 1126.556600911842, (32, 18264): 1127.3632405237802, (32, 18266): 1128.2978777966302, (32, 18267): 1129.024023807438, (32, 18268): 1129.5498480308545, (32, 18269): 1131.0454855943835, (32, 18275): 1130.3418690345313, (32, 18285): 1126.9111265684055, (32, 18308): 1111.2320777141674, (32, 18313): 1107.1842539535385, (32, 18314): 1110.4308224266083, (32, 18315): 1129.7202296262399, (32, 18316): 1130.215702726569, (32, 18317): 1130.9532312901706, (32, 18320): 1130.772142944023, (32, 18321): 1131.4502256656592, (32, 18322): 1132.4893247309872, (32, 18324): 1132.4741034043625, (32, 18325): 1134.8666054277446, (32, 18326): 1133.9474525382257, (32, 18327): 1132.1347020772992, (32, 18329): 1135.2679579563949, (32, 18330): 1135.9493664995764, (32, 18331): 1134.051188888071, (32, 18332): 1132.4081990996376, (32, 18333): 1135.162546005766, (32, 18336): 1132.9170348977636, (32, 18337): 1133.3449178019662, (32, 18403): 1135.5310215465545, (32, 18432): 1120.9066690236727, (32, 18451): 1130.8524841189846, (32, 18466): 1139.1201269630878, (32, 18481): 1128.7416919191494, (32, 18483): 1129.1688096136784, (32, 18484): 1127.5235457629021, (32, 18485): 1122.133610167166, (32, 18486): 1124.1337934745227, (32, 18487): 1120.5462737137602, (32, 18489): 1125.2243942236687, (32, 18490): 1127.1158893329016, (32, 18491): 1128.5578565844146, (32, 18492): 1117.8258072369895, (32, 18493): 1123.1068969899284, (32, 18494): 1124.9872355046584, (32, 18495): 1125.9768201398022, (32, 18496): 1124.8189954578377, (32, 18497): 1119.320786030842, (32, 18498): 1121.7820781355717, (32, 18499): 1124.1903990834428, (32, 18501): 1121.684067571679, (32, 18502): 1120.0932519729997, (32, 18503): 1119.3992672778197, (32, 18504): 1125.9477892553653, (32, 18506): 1120.67223010836, (32, 18507): 1118.9090726020654, (32, 18508): 1123.4358044101562, (32, 18509): 1123.0566648873619, (32, 18510): 1118.8338571391146, (32, 18511): 1122.6899366021298, (32, 18512): 1121.6947275420289, (32, 18515): 1125.4800473160183, (32, 18516): 1124.1808569327143, (32, 18517): 1121.5530498532103, (32, 18518): 1125.8277258085861, (32, 18519): 1126.5286529340199, (32, 18520): 1123.4983593878865, (32, 18522): 1133.8557755087945, (32, 18523): 1133.7061347337446, (32, 18532): 1135.1117464495624, (32, 18535): 1131.7069884222608, (32, 18537): 1129.8122321280866, (32, 18539): 1129.960899104843, (32, 18540): 1129.9198540332159, (32, 18541): 1130.6367374201066, (32, 18542): 1131.1372005095404, (32, 18543): 1128.4585682973375, (32, 18546): 1128.9258795377596, (32, 18555): 1131.8552952196712, (32, 18556): 1132.066216228307, (32, 18565): 1134.2538416536506, (32, 18567): 1134.1813643111304, (32, 18568): 1132.9800400904217, (32, 18577): 1144.6648714543367, (32, 18583): 1144.0004351279053, (32, 18605): 1148.0186837631297, (32, 18608): 1133.2917188926574, (32, 18616): 1158.8436521772576, (32, 18618): 1167.2555489241647, (32, 18625): 1167.5273338740083, (32, 18645): 1160.770029678184, (32, 18646): 1161.7617641262916, (32, 18653): 1150.734226683158, (32, 18654): 1158.044715441788, (32, 18655): 1152.5294069501474, (32, 18666): 1188.433566855891, (32, 18837): 1208.0089091998425, (32, 18974): 1142.0147520283638, (32, 18999): 1155.845239760498, (32, 19000): 1158.7525123749413, (32, 19174): 1061.042675084394, (32, 19342): 1129.233230988263, (32, 19455): 1053.5186284294969, (32, 19555): 941.4148423930376, (32, 19564): 969.5531966023467, (32, 19573): 959.5805109841161, (32, 19586): 953.7940701474377, (32, 19605): 952.6140908120458, (32, 19611): 958.5753170333857, (32, 19614): 950.3078632766255, (32, 19641): 1025.6986709577386, (32, 19702): 1030.5160538463115, (32, 19713): 1023.7072963373214, (32, 19731): 889.8624064648698, (32, 19819): 1043.8463712501166, (32, 19893): 648.78264072335, (32, 19899): 672.9937034137298, (32, 19929): 657.8516121693123, (32, 19951): 716.8054141712354, (32, 19962): 657.1194814255695, (32, 19970): 680.8774133703712, (32, 19971): 678.5608499708455, (32, 19972): 671.8037492155445, (32, 19975): 671.3215203998544, (32, 19978): 740.0527399998408, (32, 19987): 742.7025822115313, (32, 19989): 726.2492660003151, (32, 20039): 746.5425288012767, (32, 20043): 755.7273447324989, (32, 20047): 752.4485118300037, (32, 20052): 732.4480800801682, (32, 20054): 732.7487538849558, (32, 20085): 831.4182871927378, (32, 20104): 837.2240395978339, (32, 20132): 799.5658631985375, (32, 20203): 622.8687314136217, (32, 20280): 609.30106767399, (32, 20285): 604.860239944714, (32, 20290): 613.5903562861404, (32, 20297): 608.1945962352607, (32, 20309): 728.7426254184577, (32, 20453): 835.0108618714158, (32, 20485): 574.6175297835405, (32, 20520): 562.3038088963024, (32, 20526): 548.9452271953696, (32, 20698): 1050.8366610711892, (32, 20868): 1167.0782423638734, (32, 21042): 598.6440912384265, (32, 21057): 636.8242518742221, (32, 21066): 611.8961101241999, (32, 21075): 613.5831429020154, (32, 21093): 592.8614840209934, (32, 21098): 607.9193665175002, (32, 21127): 597.148034119622, (32, 21130): 600.10870430929, (32, 21144): 607.1097780269089, (32, 21146): 594.7278113546497, (32, 21147): 608.9177533571179, (32, 21148): 612.6044278095382, (32, 21153): 629.609249075386, (32, 21293): 651.2792403691867, (32, 21426): 718.5922687758042, (32, 21442): 771.9703291775876, (32, 21451): 776.7688211547726, (32, 21466): 740.9571529148923, (32, 21469): 745.0588012133193, (32, 21471): 739.0620445704037, (32, 21473): 741.4844757282386, (32, 21475): 738.2624331209902, (32, 21482): 750.802838699207, (32, 21484): 748.2899519664961, (32, 21488): 746.7335511563665, (32, 21494): 733.8428345836987, (32, 21498): 738.0225550734538, (32, 21500): 727.9475805942345, (32, 21514): 722.2555398242345, (32, 21537): 717.1279928304912, (32, 21662): 715.8583390610025, (32, 21691): 695.2294814605606, (32, 21757): 693.7485923019226, (32, 21777): 500.6078575544247, (32, 21778): 495.79916091846366, (32, 21779): 494.14349331808626, (32, 21790): 510.737068047427, (32, 21802): 502.06625228364464, (32, 21824): 502.98893809663394, (32, 21874): 490.1179389876674, (32, 21879): 479.36845943994285, (32, 21983): 543.4103307794651, (32, 22002): 570.6936007353788, (32, 22132): 634.1904412551556, (32, 22261): 519.9747475306208, (32, 22298): 502.7125423034869, (32, 22339): 570.8680577856773, (32, 22508): 397.97093304436106, (32, 22841): 2198.2180006084054, (32, 22842): 2197.4200659777753, (32, 22874): 2178.722403246761, (32, 22941): 2183.1758788765596, (32, 22956): 2192.139042794202, (32, 22960): 2196.986641636055, (32, 22968): 2195.166390891266, (32, 22970): 2199.464379700528, (32, 22974): 2197.0675687648168, (32, 22980): 2208.628346563986, (32, 23025): 2197.1167121029816, (32, 23028): 2192.3908131553885, (32, 23081): 2199.0358297717075, (32, 23104): 2160.4511208956355, (32, 23147): 2087.812628062634, (32, 23298): 796.583109930792, (32, 23376): 778.7962999000403, (32, 23381): 751.6748883760453, (32, 23529): 794.8006827710133, (32, 23556): 786.4443363940709, (32, 23718): 799.5146526264944, (32, 24001): 906.6380772093302, (32, 24094): 915.6895111369537, (32, 24129): 934.0973474399575, (32, 24174): 886.3643608861144, (32, 24235): 921.2825564769391, (32, 24259): 944.985792234843, (32, 24260): 942.7440030104113, (32, 24261): 939.6397386604336, (32, 24305): 968.6196435733854, (32, 24306): 970.9926271018933, (32, 24307): 966.2974357740161, (32, 24308): 968.4715331788212, (32, 24498): 1033.2543347513533, (32, 24499): 1033.2257527893955, (32, 24500): 1030.2872771453806, (32, 24668): 1030.98688283583, (32, 24711): 1046.6369853734027, (32, 24756): 1051.5730647112343, (32, 24788): 1059.9554118508836, (32, 24809): 1032.0924528022736, (32, 24813): 1041.391547857531, (32, 24821): 1038.6107295927116, (32, 24825): 1039.4856850217907, (32, 24832): 1031.1508542986362, (32, 24833): 1034.7190846203212, (32, 24835): 1037.9155384901792, (32, 24837): 1044.4312464191928, (32, 24840): 1030.1672257674527, (32, 24841): 1036.573458833111, (32, 24844): 1029.7467566689545, (32, 24845): 1035.2780732049703, (32, 24846): 1031.7633708414596, (32, 24849): 1033.4303501199931, (32, 24850): 1041.7680569364531, (32, 24863): 996.4233736302573, (32, 24866): 1003.015487841932, (32, 24885): 1008.5968077005282, (32, 24886): 1007.8714099317051, (32, 24889): 1026.456269493527, (32, 24903): 1033.8934775854293, (32, 24909): 1013.7615994956974, (32, 24999): 1304.008773301048, (32, 25019): 1301.2963909796385, (32, 25028): 1299.2048568731884, (32, 25137): 601.6250538208652, (32, 25145): 609.2933677557331, (32, 25208): 686.9466550723755, (32, 25233): 676.4482359457547, (32, 25371): 612.5883051113399, (32, 25377): 594.7344806564614, (32, 25828): 233.29049487475137, (32, 25851): 208.3773883286441, (32, 25874): 243.6814572085427, (32, 25898): 247.982412423305, (32, 25946): 229.2746020954177, (32, 26047): 319.507216892769, (32, 26066): 503.4635508509041, (32, 26197): 391.08911443372324, (32, 26212): 14.503898433036106, (32, 26253): 8.994891489212556, (32, 26254): 6.4816048532542565, (32, 26257): 5.769963678709684, (32, 26258): 4.987986746323206, (32, 26260): 1.3323048498326158, (32, 26266): 17.777150640823304, (32, 26267): 15.134304731127404, (32, 26271): 12.89713078635014, (32, 26304): 87.723580445843, (32, 26305): 90.8040803317021, (32, 26363): 197.45985114522844, (32, 26441): 499.19029355320083, (32, 26442): 497.5503685606166, (32, 26450): 486.53789927087075, (32, 26459): 483.2798384712923, (32, 26462): 483.8363848611898, (32, 26467): 515.791957024817, (32, 26471): 507.93968856614225, (32, 26472): 507.3267388592618, (32, 26473): 507.28846335411436, (32, 26476): 505.8699844438871, (32, 26485): 489.85924800205737, (32, 26493): 491.45320039218666, (32, 26524): 487.69116762880265, (32, 26525): 487.006969151342, (32, 26556): 503.51230625847705, (32, 26560): 500.66412941782534, (32, 26561): 493.35843269379524, (32, 26564): 501.08457102570065, (32, 26569): 492.2398726206787, (32, 26570): 490.16690054230594, (32, 26573): 492.92256927391685, (32, 26581): 493.6085315199992, (32, 26583): 490.63840326940215, (32, 26593): 494.9273027796713, (32, 26837): 518.8512000735541, (32, 26844): 525.7346148473482, (32, 26863): 513.1321044437905, (32, 26893): 533.7514075453032, (32, 26902): 543.117737660458, (32, 26905): 531.5697438155412, (32, 26912): 539.5470703303977, (32, 26921): 522.8553106708678, (32, 26922): 508.05700806024015, (32, 27212): 566.9983080938996, (32, 27218): 559.954791369781, (32, 27239): 580.6269534869134, (32, 27257): 572.7987207856338, (32, 27274): 583.1504595889672, (32, 27279): 580.9897062328286, (32, 27282): 572.7885570832676, (32, 27283): 577.2197261283912, (32, 27285): 586.5023433002556, (32, 27286): 577.9684565386635, (32, 27290): 565.6807672710725, (32, 27295): 561.5551987207317, (32, 27300): 584.8057236754059, (32, 27344): 560.214892668722, (32, 27366): 569.004267959591, (32, 27383): 586.0146702164932, (32, 27398): 597.4261991061305, (32, 27406): 589.7123253254397, (32, 27407): 592.628241244148, (32, 27426): 586.6325837591116, (32, 27432): 549.8404833134515, (32, 27460): 573.5990282666249, (32, 27523): 566.2478616165172, (32, 27545): 718.6867858067303, (32, 27602): 903.5876716844236, (32, 27606): 907.33027453618, (32, 27646): 707.8222900656083, (32, 27667): 745.4407815251626, (32, 27672): 747.4474857123137, (32, 27674): 741.0128967756899, (32, 27688): 746.5841376711028, (32, 27692): 753.9175274356875, (32, 27693): 748.279427330988, (32, 27705): 747.9600078983406, (32, 27712): 750.7211983757712, (32, 27786): 923.901572252902, (32, 27790): 909.5358981577233, (32, 27791): 908.8291092765053, (32, 27795): 913.0436120246278, (32, 27801): 901.5742373459984, (32, 27813): 928.9555078843239, (32, 27816): 923.3448724960282, (32, 27823): 901.2125358755824, (32, 27830): 916.5685894446289, (32, 27884): 645.0513571423016, (32, 27885): 691.9622207451874, (32, 27896): 663.5076823244883, (32, 27919): 661.5459466014582, (32, 27922): 667.403219800727, (32, 27930): 652.0859218889098, (32, 27934): 653.9071755808822, (32, 27935): 655.2711734778002, (32, 27948): 884.4184085249444, (32, 27951): 892.7648181235021, (32, 28061): 796.4526053967905, (32, 28290): 1146.5428503441983, (32, 28292): 1157.0527214220972, (32, 28293): 1148.8058546282857, (32, 28295): 1147.3523446258882, (32, 28296): 1147.091393903093, (32, 28297): 1141.1758497606975, (32, 28302): 1140.0136606126598, (32, 28310): 1483.811221311499, (32, 28313): 1496.2816874716204, (32, 28372): 1484.4773811964117, (32, 28398): 1486.030500979362, (32, 28399): 1484.4128617059614, (32, 28400): 1488.7060697457428, (32, 28401): 1475.8288802577401, (32, 28445): 1496.570806564044, (32, 28475): 1458.2478856462374, (32, 28885): 883.3766354913383, (32, 28886): 878.3332857483704, (32, 28915): 875.0283818719672, (32, 28916): 874.0973623131584, (32, 28917): 870.8527592832019, (32, 28921): 891.2066070197164, (32, 28931): 888.5850148915665, (32, 28945): 850.341879588192, (32, 28982): 861.4468308553431, (32, 29219): 849.2812761938159, (32, 29228): 835.0657789227217, (32, 29246): 914.690779045764, (32, 29248): 908.359814555202, (32, 29282): 890.1413053155105, (32, 29290): 929.3918113251427, (32, 29291): 924.1136087931666, (32, 29292): 928.3259459629792, (32, 29293): 920.9875081517336, (32, 29294): 924.6736001183252, (32, 29298): 920.1925772629721, (32, 29299): 918.1996895924805, (32, 29304): 914.384719015348, (32, 29317): 898.7584605493716, (32, 29323): 897.7150190890563, (32, 29330): 904.9635727073814, (32, 29331): 909.7565941748599, (32, 29344): 839.526377930792, (32, 29445): 651.1079600929332, (32, 29724): 2201.7643716568423, (32, 29738): 2204.7771385875863, (32, 29745): 2197.125063592712, (32, 29748): 2204.635234414561, (32, 29750): 2211.994212446282, (32, 29759): 2199.795835791241, (32, 29772): 2211.0234285889023, (32, 29781): 2208.737907996439, (32, 29784): 2204.337582464838, (32, 29790): 2212.2000606630277, (32, 29811): 2208.375837485039, (32, 29817): 2244.248242037844, (32, 29818): 2242.125714125474, (32, 29929): 2192.4788099724137, (32, 30039): 2215.910092269009, (32, 30066): 2181.32502913293, (32, 30116): 2090.999035383258, (32, 30238): 1957.3163747972214, (32, 30248): 2006.1206382187243, (32, 30260): 2006.1543885791846, (32, 30545): 855.0354314672092, (32, 30733): 723.957435179708, (32, 30756): 644.680247467957, (32, 30921): 729.735185830751, (32, 31079): 722.8690799011699, (32, 31149): 662.7096632231436, (32, 31154): 671.1155275417979, (32, 31160): 660.9277105337419, (32, 31163): 669.6181828933516, (32, 31189): 615.4452805415544, (32, 31215): 626.2709163750303, (32, 31259): 659.673111682885, (32, 31262): 652.2644064491908, (32, 31430): 751.3161126035955, (32, 31568): 718.431122572707, (32, 31751): 718.4193078171339, (38, 109): 1005.4819174134502, (38, 872): 2518.41156609308, (38, 873): 2526.5399565475627, (38, 877): 2523.4349549380586, (38, 879): 2524.6352167563027, (38, 884): 2516.3413567021457, (38, 889): 2521.462577195182, (38, 891): 2513.6676131868694, (38, 892): 2530.947580037813, (38, 894): 2529.944483933115, (38, 896): 2522.2039865962824, (38, 903): 2523.6752931172114, (38, 909): 2510.016951948751, (38, 910): 2513.322130501221, (38, 912): 2507.932944204476, (38, 913): 2501.97667692907, (38, 916): 2499.527227653007, (38, 926): 2516.053427631863, (38, 927): 2513.3338654433132, (38, 948): 2510.73082483713, (38, 961): 2515.646511972962, (38, 962): 2516.604307669886, (38, 963): 2517.66933009241, (38, 967): 2527.1348858507363, (38, 974): 2522.638207990609, (38, 998): 2530.3034594191035, (38, 1014): 2708.604932006388, (38, 1086): 2499.3371551035766, (38, 1087): 2498.3294047279696, (38, 1089): 2490.789749823577, (38, 1090): 2494.229112454108, (38, 1092): 2505.9940590291703, (38, 1097): 2497.016114811005, (38, 1107): 2511.862802770896, (38, 1387): 1266.0877264335554, (38, 1554): 1138.5669705783375, (38, 1827): 2886.688233146495, (38, 1828): 2887.618731434688, (38, 1829): 2888.8143649444896, (38, 1830): 2887.198160005964, (38, 1831): 2887.9846717737755, (38, 1832): 2887.1447387120365, (38, 1833): 2887.299842062651, (38, 1836): 2886.4297826958045, (38, 1841): 2891.538520575727, (38, 1843): 2889.3630129710236, (38, 1844): 2890.274665269767, (38, 1845): 2887.6343823093225, (38, 1847): 2879.4170818317434, (38, 1848): 2882.284032045338, (38, 1849): 2895.6618109944116, (38, 1850): 2897.1219380130296, (38, 1851): 2884.326008613162, (38, 1852): 2884.403694623286, (38, 1854): 2885.881439249112, (38, 1856): 2878.8358808492767, (38, 1857): 2882.0166423540086, (38, 1858): 2894.4477354387664, (38, 1861): 2888.5206545229235, (38, 1866): 2878.5386626105596, (38, 1867): 2891.7995427864557, (38, 1868): 2890.1596500306905, (38, 1870): 2889.8638630396376, (38, 1871): 2891.514891909538, (38, 1875): 2885.8251018707087, (38, 1880): 2880.7512024584516, (38, 1882): 2881.4119801098295, (38, 1883): 2897.383804732142, (38, 1889): 2882.4710394117224, (38, 1893): 2889.1823181554487, (38, 1894): 2887.179096988082, (38, 1899): 2880.760778221334, (38, 1900): 2882.307391601765, (38, 1902): 2892.7209207507854, (38, 1905): 2895.2671012744613, (38, 1907): 2884.375594694006, (38, 1910): 2885.504781828911, (38, 1917): 2901.2207915961526, (38, 1920): 2884.6864616645416, (38, 1935): 2895.8728574191614, (38, 1937): 2898.0729027313137, (38, 1946): 2876.5125580078807, (38, 1949): 2879.0884485323572, (38, 1950): 2869.950575252015, (38, 1951): 2874.2922909794547, (38, 1952): 2877.1578303843767, (38, 1953): 2878.841644186822, (38, 1954): 2876.6168737827247, (38, 1958): 2878.2416376443725, (38, 1960): 2882.4331968306496, (38, 1968): 2884.0878120980906, (38, 1969): 2896.6285446919837, (38, 1974): 2893.3282511169537, (38, 1975): 2893.216031470405, (38, 1979): 2887.2916119741762, (38, 1980): 2886.584215026026, (38, 1981): 2888.505512590172, (38, 1985): 2890.032405636317, (38, 1994): 2865.9722468550503, (38, 2011): 2881.221716195304, (38, 2019): 2902.073675842445, (38, 2020): 2899.315130668549, (38, 2029): 2888.6009338524304, (38, 2030): 2897.4068397171313, (38, 2032): 2886.72484737374, (38, 2033): 2892.5377759916455, (38, 2034): 2892.317665628884, (38, 2036): 2881.1343094820954, (38, 2037): 2884.0176006924157, (38, 2038): 2885.5107172173944, (38, 2042): 2917.703121295587, (38, 2050): 2891.2632522567746, (38, 2051): 2890.6688841088207, (38, 2053): 2891.580605829843, (38, 2054): 2894.4248744589017, (38, 2066): 2888.6138592076445, (38, 2067): 2888.698657664831, (38, 2071): 2860.656964354101, (38, 2072): 2866.095613206481, (38, 2073): 2851.714174677232, (38, 2074): 2850.9154047623147, (38, 2080): 2841.688450115737, (38, 2082): 2869.0014811220644, (38, 2083): 2871.8210022450426, (38, 2089): 2866.025947631518, (38, 2090): 2868.675445568429, (38, 2092): 2865.21227530006, (38, 2098): 2845.2947075650927, (38, 2099): 2848.3493978172905, (38, 2101): 2844.634404415374, (38, 2102): 2859.383395883427, (38, 2103): 2854.7066974859804, (38, 2104): 2852.1031601487903, (38, 2106): 2873.647685958296, (38, 2112): 2846.5054970930937, (38, 2113): 2861.42365824197, (38, 2114): 2864.811095332955, (38, 2117): 2875.7728411951107, (38, 2123): 2857.387173507541, (38, 2124): 2860.4274569086, (38, 2134): 2851.620485417063, (38, 2138): 2860.624568440852, (38, 2141): 2852.7190269528983, (38, 2148): 2856.557100264066, (38, 2150): 2845.292333180079, (38, 2151): 2848.450509570089, (38, 2152): 2843.5725272666245, (38, 2153): 2857.645920940336, (38, 2154): 2845.0889988183408, (38, 2155): 2843.5283379225543, (38, 2156): 2841.263708149612, (38, 2157): 2844.0409628906573, (38, 2160): 2864.596747988136, (38, 2161): 2842.9908765627006, (38, 2162): 2857.9226370003444, (38, 2163): 2853.674342601838, (38, 2164): 2853.346702942468, (38, 2168): 2846.219738676896, (38, 2172): 2848.7682511310272, (38, 2174): 2848.0103083020576, (38, 2178): 2851.173935864495, (38, 2179): 2849.18188615578, (38, 2183): 2860.3522519093995, (38, 2185): 2860.5088922155837, (38, 2186): 2858.1005638909346, (38, 2190): 2865.2573006992175, (38, 2192): 2860.909321103815, (38, 2193): 2861.223930547318, (38, 2194): 2856.7815448267356, (38, 2195): 2856.064925037337, (38, 2197): 2861.823736699194, (38, 2205): 2855.498473635263, (38, 2207): 2847.2899169517605, (38, 2208): 2851.865324656123, (38, 2212): 2862.679126102478, (38, 2214): 2771.5812963106982, (38, 2225): 2781.9651036532427, (38, 2231): 2762.687814332956, (38, 2278): 2825.480124168135, (38, 2284): 2834.423108562598, (38, 2285): 2833.0648280405217, (38, 2291): 2814.3664648808713, (38, 2292): 2817.012130188425, (38, 2307): 2828.4674697480405, (38, 2313): 2812.0025344917835, (38, 2317): 2810.5189256964804, (38, 2319): 2820.0917854414597, (38, 2321): 2824.177885586471, (38, 2323): 2823.810738023178, (38, 2326): 2840.1270918068635, (38, 2327): 2836.1718469727157, (38, 2329): 2833.4536405102026, (38, 2330): 2830.314520909079, (38, 2332): 2836.744744220146, (38, 2344): 2826.917735466487, (38, 2346): 2826.608455442693, (38, 2361): 2826.05859287816, (38, 2368): 2871.651312043104, (38, 2374): 2875.9096827996223, (38, 2375): 2877.4278419535904, (38, 2377): 2862.320820162626, (38, 2378): 2880.116340688136, (38, 2379): 2880.3724488272974, (38, 2380): 2881.9629501058366, (38, 2383): 2866.448700345289, (38, 2385): 2868.8371868369054, (38, 2395): 2869.2049453711807, (38, 2397): 2878.508486695208, (38, 2398): 2857.493933888904, (38, 2399): 2863.015251665037, (38, 2400): 2861.7922742957567, (38, 2402): 2870.1174633531355, (38, 2403): 2873.5021461670744, (38, 2404): 2874.427111643715, (38, 2405): 2866.2223746430564, (38, 2407): 2872.982608107022, (38, 2408): 2876.9003611000635, (38, 2409): 2868.7312931834076, (38, 2411): 2873.2578026476767, (38, 2412): 2872.452799000522, (38, 2413): 2875.1989444301907, (38, 2414): 2870.6548276473336, (38, 2422): 2872.149187203193, (38, 2424): 2873.456526488293, (38, 2426): 2874.23455063244, (38, 2433): 2867.8375950787067, (38, 2436): 2866.0130951881024, (38, 2437): 2846.2832400614943, (38, 2440): 2850.671127697639, (38, 2445): 2936.7370259293725, (38, 2447): 2926.151772699344, (38, 2454): 2936.2680724943657, (38, 2455): 2936.962991977517, (38, 2460): 2905.3716267406544, (38, 2461): 2909.2420666906987, (38, 2471): 2971.14966092162, (38, 2492): 2898.096406617328, (38, 2511): 2867.9264758523645, (38, 2523): 2883.3384881724814, (38, 2525): 2878.191186850808, (38, 2535): 2890.183614636236, (38, 2537): 2883.1224921877597, (38, 2538): 2888.173679785414, (38, 2539): 2885.2457222537596, (38, 2540): 2893.36437654533, (38, 2542): 2898.165322326658, (38, 2559): 2999.141979015229, (38, 2575): 2989.121157397665, (38, 2599): 2841.335619778807, (38, 2600): 2874.4224903298523, (38, 2607): 2855.9188990408743, (38, 2627): 2883.6533375103863, (38, 2647): 2901.2880596719315, (38, 2674): 2893.026751390332, (38, 2681): 2889.9015810332667, (38, 2683): 2899.1306059803214, (38, 2686): 2889.10476426078, (38, 2689): 3008.260663357305, (38, 2690): 3008.700917850286, (38, 2713): 3027.4973473489963, (38, 2714): 3028.903090022032, (38, 2715): 3031.8764367390086, (38, 2739): 3029.4181875210706, (38, 2740): 3012.3312231415725, (38, 2741): 3013.9263914751514, (38, 2749): 3024.6719377706777, (38, 2750): 3025.817581666422, (38, 2752): 3028.035426356404, (38, 2755): 3030.249406532403, (38, 2758): 3029.3814271229653, (38, 2759): 3029.4889916931493, (38, 2769): 3026.2828202986943, (38, 2771): 3016.6998767435202, (38, 2779): 3016.0783673883434, (38, 2784): 2981.9696860967974, (38, 2800): 2986.3825220499707, (38, 2802): 3005.7660364024828, (38, 2803): 3004.8270204999817, (38, 2804): 3002.91812138873, (38, 2805): 3007.6885501437773, (38, 2807): 3007.6977361707723, (38, 2809): 3006.1576947945705, (38, 2812): 2987.596344044986, (38, 2814): 3003.8513878103317, (38, 2817): 3002.708491841818, (38, 2819): 3008.558804197431, (38, 2823): 2987.7548075496525, (38, 2832): 3011.1015059022534, (38, 2836): 2997.7585625528313, (38, 2839): 3007.8516645053055, (38, 2841): 3004.284526013947, (38, 2843): 3003.6137364166516, (38, 2846): 2999.5995262716838, (38, 2849): 3012.852686274039, (38, 2852): 3009.9481329419996, (38, 2853): 3014.1773909181725, (38, 2876): 3014.6039949532783, (38, 2877): 3025.169631745661, (38, 2885): 3026.484263733065, (38, 2918): 3011.2878027658585, (38, 2921): 3015.6686709915452, (38, 2925): 2995.677783919538, (38, 2926): 2989.3116442541445, (38, 2930): 3002.689380848358, (38, 2931): 2997.170468780303, (38, 2938): 3011.021183603697, (38, 2940): 3025.904746763916, (38, 2947): 3010.574962521734, (38, 2949): 3003.287871731878, (38, 2950): 3005.039561136028, (38, 2952): 3002.7585385841016, (38, 2958): 3002.446630353576, (38, 2959): 3005.002852065539, (38, 2960): 3009.9407493665153, (38, 2961): 3007.366267081108, (38, 2963): 3000.3379676617596, (38, 2968): 3001.5940049277633, (38, 2976): 2999.926498867437, (38, 2981): 2954.364546025134, (38, 2982): 2952.7280911881817, (38, 2984): 2950.386345486432, (38, 3003): 2945.997320006484, (38, 3046): 2920.8046619862607, (38, 3050): 2941.9856232014185, (38, 3051): 2943.9098679487756, (38, 3053): 2938.781910072633, (38, 3069): 2965.938847520997, (38, 3071): 2938.4313845885918, (38, 3080): 3025.855192847583, (38, 3199): 2936.2294933481357, (38, 3200): 2930.7024431107975, (38, 3205): 2963.3392503707646, (38, 3209): 2933.4047473253654, (38, 3215): 2931.245712972343, (38, 3217): 2924.71209267749, (38, 3249): 2932.0683458809176, (38, 3263): 2981.4977223866945, (38, 3289): 2948.2584738715514, (38, 3301): 2949.2711822981287, (38, 3302): 2947.1223108697695, (38, 3307): 2944.247990534154, (38, 3310): 2952.082999580028, (38, 3391): 2946.544644831711, (38, 3509): 1911.4947348957571, (38, 3510): 1906.8806021048292, (38, 3511): 1910.229042431962, (38, 3512): 1907.6150986264856, (38, 3514): 1908.8017114002937, (38, 3519): 1920.960651399022, (38, 3536): 1920.119048159029, (38, 3545): 1927.636484580706, (38, 3548): 1920.9155140291334, (38, 3572): 1922.4065003483977, (38, 3581): 1915.894622707231, (38, 3583): 1913.8887684075542, (38, 3601): 1929.1947136579993, (38, 3656): 1920.6261080740255, (38, 3669): 1909.2397436254475, (38, 3670): 1913.2769364652856, (38, 3695): 1890.629354535655, (38, 3696): 1893.940225092027, (38, 3782): 1927.129080303985, (38, 3792): 1921.384862268434, (38, 3989): 100.03846035303548, (38, 4008): 123.04780478341024, (38, 4031): 133.51218360133018, (38, 4045): 113.79038381051427, (38, 4144): 104.57741157740409, (38, 4145): 69.7007189661326, (38, 4164): 92.6826310882672, (38, 4168): 80.20078532371005, (38, 4173): 76.34021313034295, (38, 4181): 61.33377311074883, (38, 4228): 61.8637616087608, (38, 4248): 37.410103904012075, (38, 4254): 143.3685348966954, (38, 4260): 137.42267493137754, (38, 4262): 132.57580811752334, (38, 4273): 130.82534705920386, (38, 4319): 240.19762758751827, (38, 4326): 241.63221982463645, (38, 4328): 239.0231828188459, (38, 4334): 238.30661068657577, (38, 4335): 241.33162338258882, (38, 4372): 1002.774943729133, (38, 4413): 1046.8495486906527, (38, 4434): 996.2306675956899, (38, 4447): 981.6625290516838, (38, 4452): 999.2448321167384, (38, 4463): 1078.835828766068, (38, 4465): 1072.8278826789206, (38, 4619): 1104.5479448874282, (38, 4645): 1096.9707467797477, (38, 4657): 1103.684326252336, (38, 4666): 1109.447120801703, (38, 4676): 1109.948587156376, (38, 4678): 1106.8300065021706, (38, 4689): 1114.5888283418324, (38, 4704): 1119.8168850779325, (38, 4726): 1287.9449393746893, (38, 4727): 1285.37385809189, (38, 4730): 1279.9487931504589, (38, 4731): 1284.4554695233596, (38, 4734): 1270.3693592061898, (38, 4735): 1270.4827455516836, (38, 4736): 1273.9200591560277, (38, 4737): 1272.6153781034786, (38, 4738): 1274.9755506970043, (38, 4756): 1278.8936736206715, (38, 4760): 1253.6071842305535, (38, 4761): 1250.0369630032492, (38, 4762): 1253.1684093466645, (38, 4765): 1256.3600777922084, (38, 4773): 1290.5522725149578, (38, 4774): 1292.3206199998172, (38, 4790): 1288.2315564721314, (38, 4795): 1284.9652311320178, (38, 4799): 1295.5836013981814, (38, 4801): 1306.5234108398306, (38, 4804): 1280.7455566028757, (38, 4805): 1278.1205511587996, (38, 4806): 1297.3323139021547, (38, 4815): 1298.4435441508715, (38, 4816): 1303.0299968372378, (38, 4817): 1308.9668120186484, (38, 4826): 1303.7008448478612, (38, 4830): 1302.0494888941384, (38, 4839): 1261.2715860583526, (38, 4840): 1265.5753005060596, (38, 4841): 1261.8404650440064, (38, 4846): 1259.2772391185692, (38, 4848): 1262.773279883372, (38, 4850): 1265.779588874433, (38, 4871): 1217.7492972237433, (38, 4883): 1244.7984522491197, (38, 4900): 1225.093772662217, (38, 4901): 1225.2316446436603, (38, 4917): 1184.2518447181849, (38, 4931): 1173.658314436118, (38, 4944): 1182.450237115052, (38, 4956): 1178.592338768022, (38, 4958): 1184.2498202608253, (38, 4959): 1186.3481436022957, (38, 4961): 1178.2860120213754, (38, 4966): 1179.4951161239674, (38, 5207): 1168.7905739780992, (38, 5272): 856.5295231508937, (38, 5283): 858.8425451920918, (38, 5287): 876.5205631880743, (38, 5289): 878.1623292666396, (38, 5293): 843.5236876878529, (38, 5295): 848.1365742448709, (38, 5296): 856.534094079871, (38, 5298): 861.1785786856742, (38, 5303): 869.9374223691469, (38, 5305): 871.8341854627984, (38, 5306): 882.4275031938135, (38, 5307): 871.7087641980698, (38, 5308): 875.3274159693362, (38, 5313): 864.6878897936733, (38, 5314): 862.5686982368965, (38, 5317): 880.811722349639, (38, 5319): 870.1798823115805, (38, 5324): 862.7142787924843, (38, 5326): 857.4460962691825, (38, 5348): 889.248927704633, (38, 5351): 902.2182166585717, (38, 5399): 891.6120970433398, (38, 5413): 923.1069610552892, (38, 5422): 884.2456286805541, (38, 5445): 883.7936215407123, (38, 5448): 882.3017154806694, (38, 5456): 890.8648511014156, (38, 5467): 894.6342237737556, (38, 5624): 854.6393284923696, (38, 5671): 793.7845236270026, (38, 5672): 788.9000140609043, (38, 5797): 855.2204582153606, (38, 5871): 1003.6723229294591, (38, 5976): 979.8219303594443, (38, 6118): 2450.300405563317, (38, 6248): 2542.6356469124694, (38, 6345): 859.9523293832738, (38, 6352): 881.696712318525, (38, 6354): 854.710966018703, (38, 6359): 850.3335617280025, (38, 6376): 878.2156096303111, (38, 6378): 857.2646483584571, (38, 6381): 852.0480997531687, (38, 6383): 864.5862042199354, (38, 6396): 854.4224848129932, (38, 6399): 859.594970975756, (38, 6408): 880.9547177020969, (38, 6409): 871.0294970812027, (38, 6419): 906.4083456779285, (38, 6422): 878.2830403895249, (38, 6423): 880.0443512098783, (38, 6424): 857.2316418530214, (38, 6439): 861.4951731861406, (38, 6464): 867.5821709301302, (38, 6465): 869.5779148067065, (38, 6469): 866.632424146383, (38, 6470): 867.9084246530036, (38, 6472): 842.9575390528853, (38, 6480): 848.043410934012, (38, 6486): 836.5296197351407, (38, 6497): 840.3560553464035, (38, 6503): 867.3358961192129, (38, 6508): 865.1320175301109, (38, 6509): 861.3225089215324, (38, 6521): 845.7635036296501, (38, 6544): 847.8862969339295, (38, 6552): 875.2867995070076, (38, 6553): 878.6634264687345, (38, 6554): 882.092175779959, (38, 6578): 869.5686261982476, (38, 6582): 872.6683477980771, (38, 6601): 868.138250727635, (38, 6609): 840.5603293309086, (38, 6610): 839.6904452344419, (38, 6611): 838.8087504720932, (38, 6614): 840.4697753078965, (38, 6615): 839.9006444116889, (38, 6616): 836.6510572373884, (38, 6617): 838.0865796455768, (38, 6618): 833.464696469693, (38, 6619): 842.9577577171029, (38, 6620): 836.745398407339, (38, 6621): 839.6485036014027, (38, 6622): 838.8580681253688, (38, 6623): 840.8904190007619, (38, 6624): 843.5826694690292, (38, 6625): 844.0528074597363, (38, 6626): 843.0794312813749, (38, 6627): 841.1091930455295, (38, 6628): 837.5330675249072, (38, 6629): 842.9693333135423, (38, 6630): 846.364562062648, (38, 6632): 843.1756044489398, (38, 6634): 849.5361437903308, (38, 6635): 840.5860616749873, (38, 6636): 836.5448292161868, (38, 6637): 846.9294807843518, (38, 6638): 846.1022274491701, (38, 6639): 840.8555485116867, (38, 6640): 845.5669491635119, (38, 6641): 839.8699291961725, (38, 6642): 846.1105361780842, (38, 6643): 843.351744741887, (38, 6645): 842.6002014171742, (38, 6646): 834.3529557638637, (38, 6647): 845.1997292320398, (38, 6653): 840.0002047038004, (38, 6655): 840.796741471241, (38, 6658): 849.7886842461381, (38, 6662): 846.368443726312, (38, 6819): 1012.8423935475635, (38, 6996): 963.7700145728422, (38, 7059): 925.9459878156302, (38, 7187): 1019.7641611738342, (38, 7304): 1079.7004951079305, (38, 7528): 977.1681941918422, (38, 7720): 746.7499599834252, (38, 7793): 756.690268609043, (38, 7807): 751.8446244677683, (38, 7808): 759.1387304335414, (38, 7831): 821.206267969041, (38, 7850): 783.415925196402, (38, 7852): 791.5236535747567, (38, 8012): 751.0381297773484, (38, 8125): 768.8291704507841, (38, 8208): 680.6180675451267, (38, 8392): 801.5499484741043, (38, 8651): 1198.0601616874906, (38, 9088): 1025.0740391130362, (38, 9443): 1311.8712436809117, (38, 9444): 1307.223733953787, (38, 9828): 1495.4437464317898, (38, 9868): 1482.335532028057, (38, 10180): 770.3856929814124, (38, 10256): 693.4522960393074, (38, 10276): 718.7122576312124, (38, 10378): 680.8642602453604, (38, 10676): 845.7869377427191, (38, 10714): 911.2983405341549, (38, 10730): 865.8773441012429, (38, 10862): 1384.614303944926, (38, 10881): 1381.1705368524135, (38, 10883): 1383.8870649464693, (38, 10885): 1384.7854250985736, (38, 10891): 1388.1661994622798, (38, 10909): 1382.8950253068492, (38, 10911): 1376.692994509451, (38, 10913): 1379.3349671384574, (38, 10915): 1376.4242586424386, (38, 10919): 1373.4666019497588, (38, 11037): 1467.6645354985758, (38, 11039): 1453.7466985858298, (38, 11516): 454.8183505745821, (38, 11856): 236.7894689077939, (38, 11857): 247.7723084095664, (38, 11861): 242.36455766694382, (38, 11881): 234.49503527839812, (38, 11902): 246.4892423547089, (38, 11911): 241.480689302357, (38, 11914): 242.85181687811993, (38, 11922): 236.3399080772373, (38, 11924): 231.5334150283586, (38, 11926): 234.54966594540667, (38, 11950): 219.31865296977043, (38, 11963): 209.28000108134745, (38, 11983): 203.5694767259233, (38, 11985): 205.2919428065249, (38, 12009): 195.2467317768079, (38, 12010): 205.4474904202094, (38, 12018): 202.69423186581992, (38, 12020): 202.28706682243103, (38, 12021): 199.8025358747153, (38, 12024): 192.88136667416265, (38, 12025): 197.60755142942273, (38, 12027): 198.61791691302008, (38, 12031): 206.7870199595359, (38, 12032): 206.0549142479401, (38, 12035): 193.09157437356194, (38, 12041): 212.00222005976732, (38, 12045): 315.36518807179345, (38, 12145): 248.44327212555098, (38, 12275): 136.6285001043171, (38, 12294): 146.21688696707102, (38, 12358): 198.9652072220278, (38, 12463): 234.99319225513375, (38, 12465): 235.19230398708163, (38, 12482): 233.1140855702764, (38, 12503): 234.56324598317937, (38, 12506): 237.10208040678268, (38, 12549): 218.036900638092, (38, 12559): 218.68139087146915, (38, 12569): 225.61156880767032, (38, 12572): 227.27017454915975, (38, 12574): 222.31726565315623, (38, 12576): 218.83026318210605, (38, 12591): 211.18626605907107, (38, 12608): 224.83171052240237, (38, 12696): 191.18939046094218, (38, 12710): 200.76199117995287, (38, 12728): 200.34907654439783, (38, 12766): 544.9026492561044, (38, 12771): 562.5233990225483, (38, 12790): 566.8986016177347, (38, 12795): 578.2525712962811, (38, 12797): 610.8736711371345, (38, 12798): 605.2646104161805, (38, 12811): 575.1089912098729, (38, 12830): 586.8857747242948, (38, 12848): 578.2724653111493, (38, 12850): 573.8634602084458, (38, 12852): 587.282600404175, (38, 12854): 591.9319414373466, (38, 12859): 572.7944114761107, (38, 12861): 599.3948506932317, (38, 12865): 570.9851968565455, (38, 12866): 572.3091938867403, (38, 12867): 564.0066314375231, (38, 12874): 568.1708552558545, (38, 12875): 564.2163630665029, (38, 12881): 579.7818954039165, (38, 12883): 573.94195832291, (38, 12885): 561.4266114854483, (38, 12888): 575.8956082506628, (38, 12889): 576.517637702695, (38, 12892): 567.5938274582882, (38, 12893): 576.4102925599374, (38, 12896): 572.9131377785243, (38, 12906): 571.271746003165, (38, 13018): 636.239945677016, (38, 13071): 642.1490780925236, (38, 13131): 656.5369571403996, (38, 13146): 622.1899836686853, (38, 13159): 690.9962054209412, (38, 13193): 661.2376086605815, (38, 13198): 709.8032337685622, (38, 13292): 645.0452180768671, (38, 13296): 621.8308074896935, (38, 13406): 753.7087000243799, (38, 13407): 756.3723818143651, (38, 13417): 768.0260558829111, (38, 13418): 763.5487434233929, (38, 13438): 733.5464274398382, (38, 13442): 726.2994463288604, (38, 13443): 731.2077812064325, (38, 13764): 1191.4791629039855, (38, 13766): 1185.3939545298942, (38, 13771): 1194.7747820920692, (38, 13783): 1191.0111670040155, (38, 13784): 1177.2913623703942, (38, 13792): 1211.7999566185943, (38, 13824): 1195.847258890703, (38, 14017): 1142.2397310069591, (38, 14870): 1266.915535127089, (38, 14997): 1049.7456552285169, (38, 15000): 1050.1876098142113, (38, 15003): 1047.334754442066, (38, 15006): 1034.0952680612345, (38, 15007): 1030.2292242864828, (38, 15056): 1033.7782434670912, (38, 15063): 1037.9236646074098, (38, 15069): 1040.4680573084954, (38, 15076): 1030.2987479893861, (38, 15086): 1041.516791444696, (38, 15087): 1047.1323963425477, (38, 15111): 1058.1085494610218, (38, 15116): 1051.893568860332, (38, 15722): 1156.8748218139012, (38, 15998): 1255.1928130528097, (38, 16073): 2075.0351855751715, (38, 16939): 2624.742405524955, (38, 16940): 2618.8199820240366, (38, 16951): 2625.0093153792436, (38, 16963): 2625.7159589357902, (38, 16965): 2633.16634978302, (38, 16969): 2631.0678601894974, (38, 16970): 2628.520692308492, (38, 16971): 2621.8281032556165, (38, 16973): 2621.179790563679, (38, 16974): 2635.9707048691735, (38, 16976): 2629.164608723068, (38, 16978): 2624.3444452307667, (38, 16980): 2631.805101832214, (38, 16982): 2635.710162313553, (38, 17045): 2820.2666798136347, (38, 17048): 2828.7712271409096, (38, 17304): 10.394848868557698, (38, 17305): 12.53002616404016, (38, 17330): 7.801112871057993, (38, 17334): 18.48388067772089, (38, 17343): 3.8458057215331993, (38, 17345): 16.279620200993623, (38, 17347): 12.095297913207009, (38, 17351): 28.804817136216506, (38, 17372): 17.43848165092333, (38, 17373): 2.6260761781799875, (38, 17377): 3.2560250838274913, (38, 17382): 10.646556027048488, (38, 17383): 9.126661743039683, (38, 17389): 14.627462923987748, (38, 17400): 5.440945575668214, (38, 17401): 6.78303236162536, (38, 17402): 4.394432070493085, (38, 17403): 3.2186769273102818, (38, 17440): 22.171045324790537, (38, 17455): 11.69565858287141, (38, 17491): 20.513963316757003, (38, 17507): 44.579925381446536, (38, 17509): 44.76093813814078, (38, 17590): 30.655360214224757, (38, 17615): 98.77951672466486, (38, 17642): 90.24887386871862, (38, 17643): 86.81681558421056, (38, 17668): 101.32554544949575, (38, 17721): 131.49898339358793, (38, 17754): 116.36444549978867, (38, 17769): 56.5681863507557, (38, 17776): 51.96617567955691, (38, 17804): 55.72883711984634, (38, 17809): 54.59268763820342, (38, 17824): 63.054121920699046, (38, 17837): 36.37407902959381, (38, 17838): 31.17508224809541, (38, 17862): 32.68709399092713, (38, 17866): 25.505985389613777, (38, 17872): 38.282263527909976, (38, 17873): 44.253487657876704, (38, 17881): 35.0395431095296, (38, 17947): 2139.8110304906654, (38, 17951): 2128.357829854935, (38, 17953): 2126.174115082773, (38, 17954): 2126.97809681762, (38, 17959): 2137.4499111218506, (38, 17963): 2133.4014599329516, (38, 18000): 2075.1328460721115, (38, 18001): 2077.4429870447125, (38, 18111): 2239.6740036415363, (38, 18148): 1948.095922361756, (38, 18166): 2061.005373763854, (38, 18189): 2166.1889394002874, (38, 18239): 2.8786912562537483, (38, 18240): 1.5354281429295586, (38, 18245): 2.3429347210442004, (38, 18247): 0.6848433638361325, (38, 18251): 1.1300753109791166, (38, 18256): 2.736283360407418, (38, 18258): 2.4069762562712254, (38, 18259): 3.1949220675739127, (38, 18260): 4.376198881680406, (38, 18262): 5.715466504038607, (38, 18263): 3.5001206800402436, (38, 18264): 4.542657689546065, (38, 18266): 7.003474860893604, (38, 18267): 7.905107226427139, (38, 18268): 8.806760722402855, (38, 18269): 10.733059811989746, (38, 18275): 9.829485214512182, (38, 18285): 3.8252840163270987, (38, 18308): 16.751155447707326, (38, 18313): 20.280767296265903, (38, 18314): 15.11021967451567, (38, 18315): 7.451699140224386, (38, 18316): 8.812374755018512, (38, 18317): 9.814753241378577, (38, 18320): 8.607423044097708, (38, 18321): 9.794803143090993, (38, 18322): 11.060567302501095, (38, 18324): 10.118221034153631, (38, 18325): 12.273831333868783, (38, 18326): 11.404639184460565, (38, 18327): 12.067094516977672, (38, 18329): 12.148290901168886, (38, 18330): 14.743900527156887, (38, 18331): 12.737265727635725, (38, 18332): 11.462147896422099, (38, 18333): 13.31608016838643, (38, 18336): 10.248684618887504, (38, 18337): 10.321703555556365, (38, 18403): 17.276180661620245, (38, 18432): 64.22782208215709, (38, 18451): 30.302337436724375, (38, 18466): 18.633929121423076, (38, 18481): 5.504766391111578, (38, 18483): 5.876557557355172, (38, 18484): 4.246972111213593, (38, 18485): 4.463579465068668, (38, 18486): 8.98839992925291, (38, 18487): 10.612452865361767, (38, 18489): 5.110161119497576, (38, 18490): 9.125585300590402, (38, 18491): 9.89835569413963, (38, 18492): 10.53370437890167, (38, 18493): 10.395663020114146, (38, 18494): 4.061366140431671, (38, 18495): 8.818678598174486, (38, 18496): 7.441157908310359, (38, 18497): 12.354761816548002, (38, 18498): 6.866646222373431, (38, 18499): 6.4456030565726525, (38, 18501): 8.946334684739336, (38, 18502): 9.688143386247003, (38, 18503): 8.805889307357171, (38, 18504): 6.3747249250273805, (38, 18506): 12.613619624203544, (38, 18507): 14.074664404143036, (38, 18508): 7.629934665133993, (38, 18509): 8.803650293713833, (38, 18510): 10.60906426774699, (38, 18511): 12.882647705516193, (38, 18512): 10.85449429454504, (38, 18515): 7.8474847227034426, (38, 18516): 11.633236587963477, (38, 18517): 13.923580407116862, (38, 18518): 10.660611551897437, (38, 18519): 5.990373745729917, (38, 18520): 6.20766607138983, (38, 18522): 10.732000184143367, (38, 18523): 10.911281816439622, (38, 18532): 12.864157469283764, (38, 18535): 8.833605008608076, (38, 18537): 6.656679626979255, (38, 18539): 7.0689375555020435, (38, 18540): 7.38250332371505, (38, 18541): 8.626474240126024, (38, 18542): 9.413569408592645, (38, 18543): 5.6896404839385655, (38, 18546): 8.246367571760171, (38, 18555): 11.875365230515715, (38, 18556): 12.968798477653596, (38, 18565): 12.870946361790121, (38, 18567): 14.812837024370122, (38, 18568): 12.379274456136523, (38, 18577): 26.53225730207819, (38, 18583): 23.290779765771205, (38, 18605): 25.94959406825674, (38, 18608): 18.99735968586129, (38, 18616): 38.81638150692101, (38, 18618): 50.32236231487141, (38, 18625): 45.93560806223154, (38, 18645): 37.565104355260964, (38, 18646): 39.1697278951558, (38, 18653): 29.727767634727154, (38, 18654): 38.70132279068274, (38, 18655): 33.03619459850097, (38, 18666): 68.04047052067335, (38, 18837): 164.19223179192244, (38, 18974): 62.6364484064061, (38, 18999): 77.68436880781191, (38, 19000): 77.59554603103827, (38, 19174): 235.47750872593184, (38, 19342): 219.37329605406768, (38, 19455): 170.09991556272303, (38, 19555): 335.41474896352315, (38, 19564): 346.25499603834334, (38, 19573): 347.8147201099682, (38, 19586): 347.3473259929139, (38, 19605): 341.99769521257844, (38, 19611): 339.947828505079, (38, 19614): 335.69903808688866, (38, 19641): 282.10567620006543, (38, 19702): 290.7718553857049, (38, 19713): 292.4915119435259, (38, 19731): 339.03476181419455, (38, 19819): 205.5445879576317, (38, 19893): 546.306034384544, (38, 19899): 558.3833801251767, (38, 19929): 541.7702019527239, (38, 19951): 543.5582729047267, (38, 19962): 555.3246553126024, (38, 19970): 526.2753322347036, (38, 19971): 532.8702058212677, (38, 19972): 537.911175680039, (38, 19975): 533.4481885678487, (38, 19978): 513.3640017917137, (38, 19987): 508.7400061419542, (38, 19989): 507.3577311310834, (38, 20039): 506.7898682728516, (38, 20043): 501.09014914868493, (38, 20047): 494.60486092108533, (38, 20052): 498.4241490931404, (38, 20054): 501.54081928465797, (38, 20085): 471.9236050999574, (38, 20104): 472.0496650939281, (38, 20132): 479.57220138295196, (38, 20203): 606.5549928525131, (38, 20280): 626.6846204291315, (38, 20285): 635.054384744621, (38, 20290): 622.599740347482, (38, 20297): 621.6659892055642, (38, 20309): 564.2483821640551, (38, 20453): 535.4708576172983, (38, 20485): 620.4584988960554, (38, 20520): 619.7526324794692, (38, 20526): 639.8987630877381, (38, 20698): 1424.5970610797276, (38, 20868): 1641.8741636865125, (38, 21042): 569.7822668040719, (38, 21057): 525.4540726570805, (38, 21066): 549.0062506043805, (38, 21075): 554.7609163209889, (38, 21093): 569.041064620657, (38, 21098): 542.0339363516199, (38, 21127): 567.4737302861274, (38, 21130): 560.4376473115857, (38, 21144): 559.2285569611056, (38, 21146): 570.3535235946787, (38, 21147): 559.2897661034544, (38, 21148): 552.4107730924153, (38, 21153): 563.9528067896465, (38, 21293): 499.95472432371696, (38, 21426): 500.97065005364664, (38, 21442): 457.6079747225728, (38, 21451): 453.4987578595491, (38, 21466): 478.56025249577885, (38, 21469): 471.6236151899387, (38, 21471): 482.0986051584569, (38, 21473): 476.25732021125566, (38, 21475): 481.3634108612926, (38, 21482): 467.6151476192322, (38, 21484): 468.85690761870603, (38, 21488): 473.03139163228, (38, 21494): 480.9725728653421, (38, 21498): 475.913848358006, (38, 21500): 483.6589062781421, (38, 21514): 469.51855752566064, (38, 21537): 484.73287455042663, (38, 21662): 464.0224449565246, (38, 21691): 490.8808293236541, (38, 21757): 538.7981251623, (38, 21777): 663.975239818262, (38, 21778): 670.5649324574696, (38, 21779): 668.5256600311149, (38, 21790): 654.8294420177957, (38, 21802): 658.3634623038222, (38, 21824): 653.266258508317, (38, 21874): 668.9294292706217, (38, 21879): 676.1040348016589, (38, 21983): 632.4126409867015, (38, 22002): 572.0101337052128, (38, 22132): 594.1753091885166, (38, 22261): 1574.8179504072327, (38, 22298): 1562.8328011540204, (38, 22339): 1648.0458637346937, (38, 22508): 1440.1943607751841, (38, 22841): 2885.6767897179025, (38, 22842): 2886.200542368107, (38, 22874): 2871.4421969329564, (38, 22941): 2871.461722729635, (38, 22956): 2881.9219863420817, (38, 22960): 2883.7058128172407, (38, 22968): 2900.192173965377, (38, 22970): 2902.016324796901, (38, 22974): 2910.991974064136, (38, 22980): 2923.101993467399, (38, 23025): 2927.468372493264, (38, 23028): 2925.8905776513716, (38, 23081): 2952.841077319814, (38, 23104): 2939.572592940918, (38, 23147): 2817.9492874585308, (38, 23298): 354.10512156152026, (38, 23376): 373.77067777266734, (38, 23381): 390.3812253689936, (38, 23529): 345.3060664844786, (38, 23556): 355.97095071622283, (38, 23718): 364.1844997120247, (38, 24001): 237.36673587502074, (38, 24094): 210.25663422414308, (38, 24129): 191.04874618012636, (38, 24174): 237.7943810923577, (38, 24235): 202.20929820271834, (38, 24259): 178.3244563955194, (38, 24260): 180.58622418956944, (38, 24261): 183.66452324672076, (38, 24305): 154.7193410571765, (38, 24306): 152.48434592204057, (38, 24307): 157.05247475573626, (38, 24308): 191.4165037858566, (38, 24498): 92.41813913345301, (38, 24499): 92.20802085610207, (38, 24500): 95.55616797094319, (38, 24668): 122.1368069985028, (38, 24711): 77.18724467814977, (38, 24756): 78.2236664133563, (38, 24788): 68.24415454189726, (38, 24809): 98.27519686167676, (38, 24813): 87.77273738009261, (38, 24821): 90.70873030833604, (38, 24825): 90.7717567130671, (38, 24832): 98.53778342299051, (38, 24833): 95.22908417428773, (38, 24835): 92.63926984854642, (38, 24837): 85.82109350668377, (38, 24840): 99.85478343777372, (38, 24841): 93.07191742989514, (38, 24844): 100.80490998755727, (38, 24845): 93.54084631849709, (38, 24846): 99.89848576577425, (38, 24849): 98.68387670154915, (38, 24850): 88.11152899239526, (38, 24863): 128.67716462885076, (38, 24866): 122.11191719661417, (38, 24885): 117.6778294952806, (38, 24886): 119.16571547982149, (38, 24889): 98.50300633080796, (38, 24903): 90.3354668852712, (38, 24909): 109.63668965785314, (38, 24999): 183.79559963864097, (38, 25019): 183.57934420889742, (38, 25028): 178.5799997203548, (38, 25137): 707.3655356968959, (38, 25145): 703.3151153438387, (38, 25208): 741.97319422689, (38, 25233): 748.396293948645, (38, 25371): 657.5414807026541, (38, 25377): 654.7077509214544, (38, 25828): 892.6829922226794, (38, 25851): 917.5386316213052, (38, 25874): 880.0089193736763, (38, 25898): 882.473542832759, (38, 25946): 895.9087785719954, (38, 26047): 854.0820654367703, (38, 26066): 642.2036429288332, (38, 26197): 759.8198379406276, (38, 26212): 1108.9039822413633, (38, 26253): 1130.5854161486834, (38, 26254): 1120.9105163774348, (38, 26257): 1117.8702144618037, (38, 26258): 1127.5425230210722, (38, 26260): 1122.227134459418, (38, 26266): 1120.2513008562878, (38, 26267): 1115.5066857636455, (38, 26271): 1116.548020876618, (38, 26304): 1035.756513527822, (38, 26305): 1033.1582562869917, (38, 26363): 933.5538835583804, (38, 26441): 1615.577142669649, (38, 26442): 1613.4888370994377, (38, 26450): 1602.5615785898585, (38, 26459): 1601.0930819658313, (38, 26462): 1602.3489587707857, (38, 26467): 1634.3081192845868, (38, 26471): 1625.6582731411481, (38, 26472): 1624.7996318347691, (38, 26473): 1624.5191533872767, (38, 26476): 1620.3077004165661, (38, 26485): 1606.8234141986193, (38, 26493): 1607.472294238757, (38, 26524): 1606.869421200093, (38, 26525): 1605.7836754915454, (38, 26556): 1621.3070407146758, (38, 26560): 1619.739037671576, (38, 26561): 1612.7113210593493, (38, 26564): 1618.498047639749, (38, 26569): 1611.1995829418865, (38, 26570): 1608.6474702428438, (38, 26573): 1610.6912113581354, (38, 26581): 1610.7038183783075, (38, 26583): 1608.1533375882075, (38, 26593): 1611.1163562634388, (38, 26837): 1636.743092892065, (38, 26844): 1643.9191911125945, (38, 26863): 1628.9468605369755, (38, 26893): 1649.8631700115238, (38, 26902): 1659.6308627237884, (38, 26905): 1649.1631937119214, (38, 26912): 1656.9725875927481, (38, 26921): 1638.9257180831073, (38, 26922): 1620.2913759407609, (38, 27212): 1671.418511215601, (38, 27218): 1661.9056242816312, (38, 27239): 1685.601649243996, (38, 27257): 1678.5410670625197, (38, 27274): 1688.5871199652192, (38, 27279): 1687.284643304548, (38, 27282): 1679.0063807797976, (38, 27283): 1681.7681799191453, (38, 27285): 1692.49151411565, (38, 27286): 1685.357786319318, (38, 27290): 1671.9730880703964, (38, 27295): 1666.482468715951, (38, 27300): 1689.9122401049226, (38, 27344): 1668.924671288128, (38, 27366): 1678.5464433611623, (38, 27383): 1693.7557326974602, (38, 27398): 1703.2246976561253, (38, 27406): 1694.8017491079017, (38, 27407): 1697.0386149439732, (38, 27426): 1684.3958174388895, (38, 27432): 1649.1233662368481, (38, 27460): 1670.9697732837908, (38, 27523): 1685.2732442106658, (38, 27545): 1827.5954174159513, (38, 27602): 2017.76835390437, (38, 27606): 2020.9175306357354, (38, 27646): 1828.5326813248744, (38, 27667): 1866.366747063327, (38, 27672): 1868.1670161555855, (38, 27674): 1861.8318660892585, (38, 27688): 1866.5060870315585, (38, 27692): 1874.9207227862873, (38, 27693): 1869.2955812407351, (38, 27705): 1869.2062013134016, (38, 27712): 1872.1469810943488, (38, 27786): 2017.2067484628355, (38, 27790): 1992.2321595948931, (38, 27791): 1989.89568587411, (38, 27795): 2006.8584056755653, (38, 27801): 1988.6083039114044, (38, 27813): 2023.4548345381982, (38, 27816): 2015.8355775113023, (38, 27823): 1987.882387833875, (38, 27830): 2006.6340445351316, (38, 27884): 1767.607026595896, (38, 27885): 1812.9794652626572, (38, 27896): 1785.440234971722, (38, 27919): 1783.345236816739, (38, 27922): 1789.295426366103, (38, 27930): 1774.243020953184, (38, 27934): 1776.163127372159, (38, 27935): 1777.6542933316732, (38, 27948): 2007.6735336096647, (38, 27951): 2015.3448394086388, (38, 28061): 1840.0580115966766, (38, 28290): 2233.980507181643, (38, 28292): 2241.6620116307126, (38, 28293): 2235.44724306185, (38, 28295): 2231.796244426307, (38, 28296): 2233.438135660068, (38, 28297): 2229.863566021325, (38, 28302): 2226.783516347709, (38, 28310): 2318.053490776462, (38, 28313): 2322.0894030127333, (38, 28372): 2327.210727191154, (38, 28398): 2327.5513653686903, (38, 28399): 2324.6937485435938, (38, 28400): 2328.8091775569687, (38, 28401): 2318.507274817438, (38, 28445): 2316.98538938113, (38, 28475): 2312.9824796675975, (38, 28885): 254.94990270526375, (38, 28886): 260.279439023612, (38, 28915): 268.5554502049039, (38, 28916): 267.3763186587975, (38, 28917): 271.1326064465093, (38, 28921): 247.58931235956769, (38, 28931): 251.11724304720832, (38, 28945): 300.74060228510035, (38, 28982): 285.28691389008213, (38, 29219): 336.2987512924527, (38, 29228): 342.0601877562671, (38, 29246): 355.7805566615293, (38, 29248): 370.14599443858134, (38, 29282): 366.7736707019175, (38, 29290): 341.46589724014143, (38, 29291): 345.22059057927584, (38, 29292): 343.76057728954373, (38, 29293): 342.8490687968249, (38, 29294): 349.63402090336723, (38, 29298): 346.6789467706503, (38, 29299): 350.4382004762163, (38, 29304): 341.3576965082077, (38, 29317): 335.81387716295063, (38, 29323): 335.0301636618743, (38, 29330): 338.0927365623241, (38, 29331): 336.60225137266144, (38, 29344): 361.82256332715605, (38, 29445): 497.1997885271922, (38, 29724): 2833.299840031513, (38, 29738): 2836.571831642395, (38, 29745): 2826.055914437802, (38, 29748): 2822.995302152645, (38, 29750): 2826.2480876860905, (38, 29759): 2819.1189507587005, (38, 29772): 2831.1305340215354, (38, 29781): 2828.3655400803077, (38, 29784): 2828.433178740196, (38, 29790): 2830.1069002008458, (38, 29811): 2821.062268114164, (38, 29817): 2830.152146618617, (38, 29818): 2827.3701984671256, (38, 29929): 2827.974716797065, (38, 30039): 2883.971958918842, (38, 30066): 2863.976632380779, (38, 30116): 2742.639329409589, (38, 30238): 2563.4463213738854, (38, 30248): 2665.2451168473162, (38, 30260): 2668.4165629640715, (38, 30545): 268.5643913001746, (38, 30733): 418.60158871069956, (38, 30756): 485.61006784765095, (38, 30921): 397.16109305755197, (38, 31079): 862.0641247077491, (38, 31149): 863.6321979652797, (38, 31154): 866.1434321371979, (38, 31160): 864.4794841407836, (38, 31163): 868.608243444123, (38, 31189): 929.0170247040181, (38, 31215): 927.6367367605761, (38, 31259): 947.9383768876785, (38, 31262): 953.6190416334853, (38, 31430): 867.3789757164727, (38, 31568): 1065.419411479043, (38, 31751): 903.1777629049827, (41, 109): 556.7091853856178, (41, 872): 2167.8103335072965, (41, 873): 2176.224372006252, (41, 877): 2174.9044664192397, (41, 879): 2176.331250607473, (41, 884): 2171.990257474013, (41, 889): 2176.3872646626432, (41, 891): 2168.716238566503, (41, 892): 2182.474091459268, (41, 894): 2180.660038101867, (41, 896): 2169.500298323448, (41, 903): 2177.317215400545, (41, 909): 2156.967181749865, (41, 910): 2158.626178099819, (41, 912): 2153.467446044077, (41, 913): 2148.4145974404255, (41, 916): 2143.7769271057773, (41, 926): 2159.139124319169, (41, 927): 2155.9336667260427, (41, 948): 2165.373734136021, (41, 961): 2162.833083322469, (41, 962): 2162.596348995064, (41, 963): 2162.7143661544587, (41, 967): 2180.1282177019225, (41, 974): 2179.8986279820433, (41, 998): 2184.9658319076484, (41, 1014): 2347.6468005097036, (41, 1086): 2096.989234098184, (41, 1087): 2089.6828452790023, (41, 1089): 2085.2568182365612, (41, 1090): 2089.2882934994204, (41, 1092): 2101.33963180461, (41, 1097): 2093.38035941782, (41, 1107): 2103.3890887968555, (41, 1387): 928.246165992107, (41, 1554): 874.0271673408431, (41, 1827): 2591.5942422681537, (41, 1828): 2591.715535731544, (41, 1829): 2593.5531523301875, (41, 1830): 2595.876110482341, (41, 1831): 2595.9857895724517, (41, 1832): 2594.715173460044, (41, 1833): 2594.1881431328775, (41, 1836): 2592.497829476217, (41, 1841): 2598.878032403877, (41, 1843): 2596.592619572293, (41, 1844): 2598.2344841180648, (41, 1845): 2596.062446789275, (41, 1847): 2585.408533064293, (41, 1848): 2588.668345980665, (41, 1849): 2604.56799541408, (41, 1850): 2605.5876275824135, (41, 1851): 2592.8370005409306, (41, 1852): 2594.52139036866, (41, 1854): 2594.9349792422677, (41, 1856): 2586.869409216826, (41, 1857): 2589.23942471747, (41, 1858): 2602.0778961175115, (41, 1861): 2594.601276514036, (41, 1866): 2587.918237410729, (41, 1867): 2597.809980757227, (41, 1868): 2594.785996534059, (41, 1870): 2599.852209922341, (41, 1871): 2596.171497430077, (41, 1875): 2593.79120986769, (41, 1880): 2587.586515223714, (41, 1882): 2590.6092200048006, (41, 1883): 2604.0602449192115, (41, 1889): 2586.8188843249495, (41, 1893): 2591.344229048106, (41, 1894): 2588.7420497728917, (41, 1899): 2583.8932919930003, (41, 1900): 2585.00684075516, (41, 1902): 2595.1380267690856, (41, 1905): 2598.9109520003108, (41, 1907): 2589.3111921933573, (41, 1910): 2588.551983503151, (41, 1917): 2600.089319151274, (41, 1920): 2588.2394675071587, (41, 1935): 2596.495000573015, (41, 1937): 2599.3757917764297, (41, 1946): 2575.7405520264947, (41, 1949): 2577.632143743972, (41, 1950): 2572.066498413436, (41, 1951): 2575.557739140833, (41, 1952): 2582.666939559259, (41, 1953): 2580.6274388262877, (41, 1954): 2581.084079482737, (41, 1958): 2578.463580015028, (41, 1960): 2583.86626960294, (41, 1968): 2585.9893191759043, (41, 1969): 2594.206802729044, (41, 1974): 2592.3134649653903, (41, 1975): 2593.2316533882918, (41, 1979): 2585.14564588478, (41, 1980): 2587.5107380820195, (41, 1981): 2587.5290515566808, (41, 1985): 2588.228154196932, (41, 1994): 2575.07276299561, (41, 2011): 2591.466593309989, (41, 2019): 2617.2810525569616, (41, 2020): 2613.889829656955, (41, 2029): 2603.770457277043, (41, 2030): 2611.494720345082, (41, 2032): 2603.5414386673224, (41, 2033): 2607.522704196776, (41, 2034): 2608.819384000917, (41, 2036): 2603.9999615740558, (41, 2037): 2605.011707848705, (41, 2038): 2599.3940249388033, (41, 2042): 2634.032612784448, (41, 2050): 2603.934324939208, (41, 2051): 2604.93939831171, (41, 2053): 2605.197905989403, (41, 2054): 2608.313231583222, (41, 2066): 2602.238533803602, (41, 2067): 2601.4878097560845, (41, 2071): 2568.5669845469506, (41, 2072): 2573.0935657697696, (41, 2073): 2553.7301475350873, (41, 2074): 2553.9307633307208, (41, 2080): 2546.859437360177, (41, 2082): 2575.873990399579, (41, 2083): 2578.1240132456446, (41, 2089): 2570.932297732526, (41, 2090): 2572.77332333085, (41, 2092): 2568.270894196082, (41, 2098): 2548.531907072142, (41, 2099): 2552.6680614808847, (41, 2101): 2549.2756018962864, (41, 2102): 2562.6764649818697, (41, 2103): 2559.003652486945, (41, 2104): 2557.6248631029466, (41, 2106): 2580.6501705298256, (41, 2112): 2552.298977720552, (41, 2113): 2565.4059006251528, (41, 2114): 2570.94650243154, (41, 2117): 2583.8496058376986, (41, 2123): 2510.0812160728756, (41, 2124): 2512.835633858738, (41, 2134): 2508.6331518354905, (41, 2138): 2515.280321485025, (41, 2141): 2508.466654305898, (41, 2148): 2526.5811031838953, (41, 2150): 2502.4399515187088, (41, 2151): 2506.3747577856343, (41, 2152): 2501.8794433881785, (41, 2153): 2526.1734454652383, (41, 2154): 2513.867865644691, (41, 2155): 2514.9273443247316, (41, 2156): 2511.1029989597255, (41, 2157): 2522.650031832473, (41, 2160): 2525.9314676874023, (41, 2161): 2502.805418766438, (41, 2162): 2531.9749182618148, (41, 2163): 2527.626873564384, (41, 2164): 2528.219157231529, (41, 2168): 2510.7903658856794, (41, 2172): 2519.8144547901134, (41, 2174): 2507.8178029132328, (41, 2178): 2523.9668752736543, (41, 2179): 2522.7135791804076, (41, 2183): 2516.7269610922567, (41, 2185): 2517.773683365612, (41, 2186): 2515.1104423100164, (41, 2190): 2524.930878879944, (41, 2192): 2520.4365847179574, (41, 2193): 2517.011353290931, (41, 2194): 2512.427099968109, (41, 2195): 2513.6374267169485, (41, 2197): 2522.335051192583, (41, 2205): 2518.562169219792, (41, 2207): 2513.0656378975746, (41, 2208): 2516.5118693628565, (41, 2212): 2514.2400062061392, (41, 2214): 2455.4738631887994, (41, 2225): 2471.1667960226414, (41, 2231): 2410.8771314692453, (41, 2278): 2526.659809814263, (41, 2284): 2538.7034162385767, (41, 2285): 2538.641369566912, (41, 2291): 2528.646101110553, (41, 2292): 2520.947249626151, (41, 2307): 2533.0422029839015, (41, 2313): 2529.5225574140327, (41, 2317): 2510.321218603659, (41, 2319): 2525.026832379857, (41, 2321): 2530.799239131216, (41, 2323): 2527.526491880017, (41, 2326): 2538.3826012199734, (41, 2327): 2534.42542557847, (41, 2329): 2532.0063300175857, (41, 2330): 2529.894289411007, (41, 2332): 2537.6908293714346, (41, 2344): 2523.6788580679918, (41, 2346): 2525.400133128634, (41, 2361): 2507.8893513625358, (41, 2368): 2563.289940769842, (41, 2374): 2569.131150971136, (41, 2375): 2569.643473048189, (41, 2377): 2552.933957444765, (41, 2378): 2573.2222176520836, (41, 2379): 2575.5228168869376, (41, 2380): 2575.683729110884, (41, 2383): 2555.8619129920485, (41, 2385): 2557.56451256419, (41, 2395): 2556.126213829002, (41, 2397): 2574.556592184324, (41, 2398): 2547.8236387715892, (41, 2399): 2552.4949889370946, (41, 2400): 2551.2083644620784, (41, 2402): 2565.3888194349825, (41, 2403): 2568.983417195719, (41, 2404): 2569.1272266182905, (41, 2405): 2561.168463159802, (41, 2407): 2566.5173326076842, (41, 2408): 2571.546796111897, (41, 2409): 2563.2838523150385, (41, 2411): 2572.1279696891115, (41, 2412): 2569.996698558894, (41, 2413): 2573.3797292394815, (41, 2414): 2569.0185489612813, (41, 2422): 2572.139203712413, (41, 2424): 2570.3152556216564, (41, 2426): 2570.4480758757177, (41, 2433): 2565.0194211687417, (41, 2436): 2565.3232319490467, (41, 2437): 2543.8982499685517, (41, 2440): 2548.052717762205, (41, 2445): 2657.07922895979, (41, 2447): 2644.00063166144, (41, 2454): 2654.589740353341, (41, 2455): 2653.686875212896, (41, 2460): 2622.8039168568603, (41, 2461): 2626.9406709197847, (41, 2471): 2700.6086042440897, (41, 2492): 2688.281541141633, (41, 2511): 2646.6588297289577, (41, 2523): 2668.157184753957, (41, 2525): 2666.330124433496, (41, 2535): 2644.903586627202, (41, 2537): 2638.722081856431, (41, 2538): 2641.540125749977, (41, 2539): 2646.6053261025477, (41, 2540): 2647.8905045485576, (41, 2542): 2654.86212537708, (41, 2559): 2738.6810030797587, (41, 2575): 2738.2801022864587, (41, 2599): 2568.9856764198253, (41, 2600): 2607.1574559421674, (41, 2607): 2579.519060981258, (41, 2627): 2691.1200786526456, (41, 2647): 2714.4802108669005, (41, 2674): 2697.4104218029984, (41, 2681): 2698.4479870407786, (41, 2683): 2705.9215057237643, (41, 2686): 2693.699137232496, (41, 2689): 2818.730563882923, (41, 2690): 2820.195335118402, (41, 2713): 2869.6215702999225, (41, 2714): 2875.156292519755, (41, 2715): 2877.9797804163068, (41, 2739): 2874.4490420824586, (41, 2740): 2846.891161963786, (41, 2741): 2847.605017043027, (41, 2749): 2874.2070611251484, (41, 2750): 2873.8595842557843, (41, 2752): 2875.3165092942522, (41, 2755): 2878.33577047597, (41, 2758): 2878.7190754673647, (41, 2759): 2878.174488558814, (41, 2769): 2873.474637488629, (41, 2771): 2854.007152634959, (41, 2779): 2863.9158596674747, (41, 2784): 2835.678127681661, (41, 2800): 2850.243764436727, (41, 2802): 2846.207720088516, (41, 2803): 2843.9894902479264, (41, 2804): 2841.6312109631613, (41, 2805): 2852.027611972656, (41, 2807): 2850.7055306626326, (41, 2809): 2852.1914678341013, (41, 2812): 2830.928935428906, (41, 2814): 2858.756954156831, (41, 2817): 2869.4963062087127, (41, 2819): 2848.2761249734776, (41, 2823): 2842.5599556083375, (41, 2832): 2857.2026509445054, (41, 2836): 2844.1352968459387, (41, 2839): 2849.5035661701036, (41, 2841): 2865.022724926555, (41, 2843): 2862.245923718828, (41, 2846): 2851.308076269682, (41, 2849): 2861.164192226085, (41, 2852): 2857.467899348516, (41, 2853): 2862.935593010209, (41, 2876): 2869.548173238879, (41, 2877): 2880.8110206018464, (41, 2885): 2894.6790138864176, (41, 2918): 2842.405844400909, (41, 2921): 2848.3049582447443, (41, 2925): 2816.8648439738276, (41, 2926): 2804.1935852249267, (41, 2930): 2838.685874079314, (41, 2931): 2822.0181096437336, (41, 2938): 2844.4667585669044, (41, 2940): 2848.180191695803, (41, 2947): 2830.1357088533946, (41, 2949): 2834.019574711445, (41, 2950): 2838.032302679027, (41, 2952): 2835.8467661690106, (41, 2958): 2834.5974822922817, (41, 2959): 2834.4750620334394, (41, 2960): 2840.239187139928, (41, 2961): 2838.742927087515, (41, 2963): 2833.8392979772802, (41, 2968): 2836.438364435551, (41, 2976): 2832.0452826800556, (41, 2981): 2803.801609286874, (41, 2982): 2804.9220866678716, (41, 2984): 2803.275869438494, (41, 3003): 2802.019038758084, (41, 3046): 2746.6668110824426, (41, 3050): 2781.875744948021, (41, 3051): 2782.707010165557, (41, 3053): 2778.880684810253, (41, 3069): 2809.6666531788605, (41, 3071): 2772.3447407303797, (41, 3080): 2898.5787501228438, (41, 3199): 2809.052006639304, (41, 3200): 2805.599225815159, (41, 3205): 2835.1537635068867, (41, 3209): 2808.4751052512634, (41, 3215): 2804.6355283991516, (41, 3217): 2798.826463108232, (41, 3249): 2803.823692522096, (41, 3263): 2847.1545533999324, (41, 3289): 2814.0694819505316, (41, 3301): 2818.788707487445, (41, 3302): 2815.4711670704232, (41, 3307): 2812.509350891431, (41, 3310): 2821.294637774037, (41, 3391): 2888.877164917311, (41, 3509): 1819.5999833679296, (41, 3510): 1815.5272028053482, (41, 3511): 1816.4052745466226, (41, 3512): 1812.2781127740373, (41, 3514): 1811.6771991925857, (41, 3519): 1838.0944936451447, (41, 3536): 1823.561648656618, (41, 3545): 1828.1071669715773, (41, 3548): 1819.4481844184913, (41, 3572): 1828.1047070681993, (41, 3581): 1829.2639162094397, (41, 3583): 1818.9573476219732, (41, 3601): 1848.5769987560063, (41, 3656): 1848.8948413694663, (41, 3669): 1855.8262519635414, (41, 3670): 1860.1153334511182, (41, 3695): 1833.0130847831683, (41, 3696): 1835.6351869880955, (41, 3782): 1788.7135241747726, (41, 3792): 1789.1900153634624, (41, 3989): 1207.780951075981, (41, 4008): 1227.2742634797494, (41, 4031): 1240.6334121571085, (41, 4045): 1219.750930487376, (41, 4144): 1206.989836227691, (41, 4145): 1172.3537430386536, (41, 4164): 1195.9010455852838, (41, 4168): 1182.7702307761178, (41, 4173): 1177.9957367304214, (41, 4181): 1166.322411519915, (41, 4228): 1171.429342862014, (41, 4248): 1144.9874468778946, (41, 4254): 977.5231516550464, (41, 4260): 985.4759577317653, (41, 4262): 986.5607407628563, (41, 4273): 990.119031758512, (41, 4319): 894.7102518235062, (41, 4326): 894.726039053463, (41, 4328): 897.6023016471652, (41, 4334): 894.8327588991885, (41, 4335): 892.0639671682155, (41, 4372): 135.81982140167557, (41, 4413): 63.525231896953954, (41, 4434): 142.53729956897396, (41, 4447): 147.52011691353815, (41, 4452): 139.7059128167121, (41, 4463): 262.23721446255877, (41, 4465): 256.97905746335323, (41, 4619): 13.40097378841462, (41, 4645): 14.58508335482367, (41, 4657): 6.597967185241144, (41, 4666): 5.546496191578427, (41, 4676): 6.6999644410554575, (41, 4678): 10.615984146346475, (41, 4689): 4.893757793133798, (41, 4704): 60.94752502355463, (41, 4726): 234.65692312523532, (41, 4727): 231.56212867727785, (41, 4730): 225.33683161275522, (41, 4731): 228.60795647834203, (41, 4734): 223.9480188451769, (41, 4735): 222.16463785871676, (41, 4736): 224.64801012744186, (41, 4737): 220.8579051801106, (41, 4738): 222.4004221715849, (41, 4756): 226.14568616102048, (41, 4760): 204.97850603003604, (41, 4761): 204.64256130840437, (41, 4762): 202.07972648527172, (41, 4765): 207.13636572812803, (41, 4773): 239.52756038229091, (41, 4774): 238.751539955134, (41, 4790): 237.18148487799473, (41, 4795): 233.99754473980508, (41, 4799): 241.16354911556465, (41, 4801): 250.49591401444326, (41, 4804): 232.69016696886095, (41, 4805): 230.12465015087187, (41, 4806): 240.60998082136567, (41, 4815): 239.51606077917074, (41, 4816): 246.29323381891726, (41, 4817): 250.30843150887756, (41, 4826): 244.92286809322485, (41, 4830): 241.60253075985273, (41, 4839): 214.03566011578292, (41, 4840): 217.6429940881409, (41, 4841): 211.8664047474568, (41, 4846): 209.38662302152187, (41, 4848): 210.47879821376597, (41, 4850): 213.5936746662643, (41, 4871): 170.59441432226316, (41, 4883): 199.148338308745, (41, 4900): 182.42739118455307, (41, 4901): 179.74573565628106, (41, 4917): 83.76993760366001, (41, 4931): 84.32475621583647, (41, 4944): 80.8752522017969, (41, 4956): 86.81499089037925, (41, 4958): 92.76843863879564, (41, 4959): 97.14754943413084, (41, 4961): 84.08999673810737, (41, 4966): 90.76635784567505, (41, 5207): 97.01464049392476, (41, 5272): 498.06047938040336, (41, 5283): 489.58062441463056, (41, 5287): 468.7253489190327, (41, 5289): 464.75528176149925, (41, 5293): 504.14414556623285, (41, 5295): 481.53122076206546, (41, 5296): 476.8934186309605, (41, 5298): 474.5490954161896, (41, 5303): 463.9589280279225, (41, 5305): 494.0008342849556, (41, 5306): 494.2600289477682, (41, 5307): 497.83997096313016, (41, 5308): 488.8535168441754, (41, 5313): 494.764938232611, (41, 5314): 491.35884524754084, (41, 5317): 486.0158303861322, (41, 5319): 470.655917306554, (41, 5324): 478.69096850878316, (41, 5326): 484.1815081458943, (41, 5348): 492.61138796942896, (41, 5351): 481.1286903673839, (41, 5399): 454.0164752986448, (41, 5413): 462.85566040198836, (41, 5422): 453.8180679192969, (41, 5445): 470.32760600639494, (41, 5448): 477.9214551013976, (41, 5456): 475.33244063576836, (41, 5467): 467.14438765876616, (41, 5624): 565.2315238681363, (41, 5671): 398.5089895667825, (41, 5672): 409.17180139620973, (41, 5797): 280.45513832645304, (41, 5871): 318.77521973963684, (41, 5976): 405.1504929162862, (41, 6118): 2452.8166645700835, (41, 6248): 2586.0440153114946, (41, 6345): 1188.2624245766326, (41, 6352): 1206.0495907943127, (41, 6354): 1181.6707030931136, (41, 6359): 1182.2111513958414, (41, 6376): 1213.0234475826387, (41, 6378): 1184.23166956877, (41, 6381): 1186.4643916577354, (41, 6383): 1190.4154290881424, (41, 6396): 1204.4743929575093, (41, 6399): 1192.8999990549255, (41, 6408): 1201.3966359359597, (41, 6409): 1182.4041890094463, (41, 6419): 1194.9229381324328, (41, 6422): 1190.72169268025, (41, 6423): 1191.5750316750134, (41, 6424): 1171.4245755882264, (41, 6439): 1171.3925739631773, (41, 6464): 1172.9931589638609, (41, 6465): 1178.4181947863356, (41, 6469): 1183.9178134673334, (41, 6470): 1186.786692203426, (41, 6472): 1177.8236520905593, (41, 6480): 1163.6725190795871, (41, 6486): 1134.2482074516643, (41, 6497): 1143.213318040965, (41, 6503): 1150.3647484478654, (41, 6508): 1160.7233824172947, (41, 6509): 1151.9909727770555, (41, 6521): 1153.4615845562973, (41, 6544): 1143.4585665425504, (41, 6552): 1168.7562752431502, (41, 6553): 1170.3646163973638, (41, 6554): 1172.1556554302965, (41, 6578): 1167.7031828194495, (41, 6582): 1157.5296115491801, (41, 6601): 1164.4862932763842, (41, 6609): 1161.4800756710533, (41, 6610): 1158.4498933754924, (41, 6611): 1164.493666688522, (41, 6614): 1169.3366909316235, (41, 6615): 1166.7409812701503, (41, 6616): 1156.3578305959488, (41, 6617): 1160.1939993606356, (41, 6618): 1148.8337786912864, (41, 6619): 1169.4638072226023, (41, 6620): 1152.3135814418363, (41, 6621): 1153.1755244834944, (41, 6622): 1155.552041517778, (41, 6623): 1165.164805241315, (41, 6624): 1162.4837806347823, (41, 6625): 1164.949051501017, (41, 6626): 1171.297109046721, (41, 6627): 1173.230603716653, (41, 6628): 1148.5829120421465, (41, 6629): 1157.1163495504716, (41, 6630): 1172.7770111043924, (41, 6632): 1159.5054790144966, (41, 6634): 1172.0506468673423, (41, 6635): 1155.9411752240014, (41, 6636): 1154.8775694970911, (41, 6637): 1158.9962282136744, (41, 6638): 1168.784323280111, (41, 6639): 1170.7324817530168, (41, 6640): 1170.5138949917625, (41, 6641): 1150.0863550997967, (41, 6642): 1166.0941167738913, (41, 6643): 1174.322698889505, (41, 6645): 1167.4176354675583, (41, 6646): 1152.5930884339525, (41, 6647): 1167.058636863461, (41, 6653): 1168.0454036825681, (41, 6655): 1172.008003144855, (41, 6658): 1170.6229959973887, (41, 6662): 1163.3433966325342, (41, 6819): 1216.339083822746, (41, 6996): 1123.0925390261368, (41, 7059): 1099.8803809698895, (41, 7187): 1020.2180211108432, (41, 7304): 1145.141653169204, (41, 7528): 1071.7030218376544, (41, 7720): 986.9377515430758, (41, 7793): 966.3715208986675, (41, 7807): 972.2581805512717, (41, 7808): 961.6672648585873, (41, 7831): 1121.841055161865, (41, 7850): 1122.854486109535, (41, 7852): 1132.8407010351482, (41, 8012): 1024.4454399565852, (41, 8125): 851.0420669095647, (41, 8208): 949.8367317133667, (41, 8392): 1043.2070798397435, (41, 8651): 1335.2717668025164, (41, 9088): 1296.2584077577092, (41, 9443): 1241.0364571221426, (41, 9444): 1234.4260253295975, (41, 9828): 1322.7197330514168, (41, 9868): 1380.1921726904093, (41, 10180): 838.8021924524127, (41, 10256): 777.2605972956375, (41, 10276): 823.3941197802178, (41, 10378): 879.1891655204672, (41, 10676): 773.1364500267621, (41, 10714): 796.6684976694959, (41, 10730): 847.6941817499686, (41, 10862): 639.1923821000181, (41, 10881): 625.103825850715, (41, 10883): 627.7225703251985, (41, 10885): 641.9704805786295, (41, 10891): 631.8063637456141, (41, 10909): 630.5096708882458, (41, 10911): 625.9847597061754, (41, 10913): 630.060688264722, (41, 10915): 628.9121973619399, (41, 10919): 625.8627895258993, (41, 11037): 751.5653401967013, (41, 11039): 776.0198038354782, (41, 11516): 1556.2329710775405, (41, 11856): 895.289727741399, (41, 11857): 883.3649838380038, (41, 11861): 889.1176441247044, (41, 11881): 902.2830118115797, (41, 11902): 898.7970530147852, (41, 11911): 908.9489326225186, (41, 11914): 904.7190139344141, (41, 11922): 903.5397059755464, (41, 11924): 907.1547010495622, (41, 11926): 906.7584189159718, (41, 11950): 920.6402194782377, (41, 11963): 922.5923250329114, (41, 11983): 939.5641114313511, (41, 11985): 922.6914374779236, (41, 12009): 938.4201495663358, (41, 12010): 932.8464418117725, (41, 12018): 935.3020874740276, (41, 12020): 933.3899518649723, (41, 12021): 935.4535367287383, (41, 12024): 937.1193862383368, (41, 12025): 933.2167669405662, (41, 12027): 933.6449460797177, (41, 12031): 932.4858481188228, (41, 12032): 930.4440286693982, (41, 12035): 942.0595766986025, (41, 12041): 913.3202203383179, (41, 12045): 916.7567149018157, (41, 12145): 937.2909427573162, (41, 12275): 1246.0280226608145, (41, 12294): 1253.6562511171915, (41, 12358): 1303.6079489059157, (41, 12463): 1335.5422108488094, (41, 12465): 1336.1559136989429, (41, 12482): 1326.8449181706847, (41, 12503): 1329.8705941280161, (41, 12506): 1331.1708386947284, (41, 12549): 1309.9382547475304, (41, 12559): 1312.6540673694135, (41, 12569): 1320.2402405723483, (41, 12572): 1320.8287520022654, (41, 12574): 1317.5708086488646, (41, 12576): 1308.8141460344625, (41, 12591): 1297.9363092464534, (41, 12608): 1297.6545251289845, (41, 12696): 1278.6966352237812, (41, 12710): 1271.2899342159192, (41, 12728): 1283.1883456506403, (41, 12766): 1179.028017527122, (41, 12771): 1142.1782975724677, (41, 12790): 1143.6685792071542, (41, 12795): 1151.8023126522648, (41, 12797): 1130.044243104013, (41, 12798): 1128.4274146118407, (41, 12811): 1130.2011004695582, (41, 12830): 1136.5587965994835, (41, 12848): 1122.5858766355675, (41, 12850): 1114.1137643218024, (41, 12852): 1132.215067897505, (41, 12854): 1132.0737675084304, (41, 12859): 1118.9978643412933, (41, 12861): 1125.3384036887644, (41, 12865): 1136.7667557337534, (41, 12866): 1132.4377703530479, (41, 12867): 1136.7112284086138, (41, 12874): 1135.2146975000574, (41, 12875): 1133.5937446069063, (41, 12881): 1137.7386652431649, (41, 12883): 1137.500298605291, (41, 12885): 1134.7249265866642, (41, 12888): 1134.6090820233685, (41, 12889): 1131.8088527385362, (41, 12892): 1136.8866054442992, (41, 12893): 1137.507305368479, (41, 12896): 1134.6891637108433, (41, 12906): 1148.0802390625013, (41, 13018): 1222.2436706635456, (41, 13071): 1238.7282930367703, (41, 13131): 1175.0128118983152, (41, 13146): 1159.2563244383286, (41, 13159): 1247.082548889245, (41, 13193): 1170.6976076465114, (41, 13198): 1150.1277272104876, (41, 13292): 1134.3017931081736, (41, 13296): 1103.013454010362, (41, 13406): 1201.0873256844475, (41, 13407): 1205.0055948049696, (41, 13417): 1234.1030205054028, (41, 13418): 1237.6022377734948, (41, 13438): 1210.9814608402173, (41, 13442): 1200.623981666523, (41, 13443): 1202.6785921999488, (41, 13764): 1539.0837447578565, (41, 13766): 1535.7740776182777, (41, 13771): 1548.3421857395924, (41, 13783): 1526.2861982469656, (41, 13784): 1528.136418766275, (41, 13792): 1568.7404761193545, (41, 13824): 1530.4522820033346, (41, 14017): 1456.3682262833306, (41, 14870): 600.0211761605433, (41, 14997): 1030.927717495561, (41, 15000): 1025.7761113986703, (41, 15003): 1018.1552695494507, (41, 15006): 1032.7984021367968, (41, 15007): 1029.4439820184773, (41, 15056): 1015.4122885996285, (41, 15063): 1015.1828341142401, (41, 15069): 1010.7306771235203, (41, 15076): 1025.577045376302, (41, 15086): 1040.7332995856925, (41, 15087): 1037.1551730978872, (41, 15111): 1050.6414188936135, (41, 15116): 1042.4088737503089, (41, 15722): 1125.8809495992782, (41, 15998): 1076.0664077265767, (41, 16073): 2237.629067530675, (41, 16939): 2385.9773891375903, (41, 16940): 2379.5361410325027, (41, 16951): 2391.947108489448, (41, 16963): 2391.312735733388, (41, 16965): 2396.91777570518, (41, 16969): 2398.2042006825873, (41, 16970): 2392.354816342235, (41, 16971): 2387.1205472603083, (41, 16973): 2388.5975638242467, (41, 16974): 2400.9243138205948, (41, 16976): 2391.6019837576264, (41, 16978): 2387.1364653847295, (41, 16980): 2391.977605466728, (41, 16982): 2402.789745774325, (41, 17045): 2718.1674381659736, (41, 17048): 2726.199282065406, (41, 17304): 1099.8785777175676, (41, 17305): 1108.1240843993085, (41, 17330): 1106.8916784387873, (41, 17334): 1093.920398081241, (41, 17343): 1112.0704722306116, (41, 17345): 1104.6354436680745, (41, 17347): 1113.6592901993208, (41, 17351): 1088.4221932393903, (41, 17372): 1097.5822518256377, (41, 17373): 1110.1744774204237, (41, 17377): 1111.9493946223047, (41, 17382): 1106.0234241328903, (41, 17383): 1103.4877866593013, (41, 17389): 1100.8895851318487, (41, 17400): 1105.1201087141694, (41, 17401): 1103.2809184533414, (41, 17402): 1106.5167082427654, (41, 17403): 1107.9871257713523, (41, 17440): 1116.7013663092832, (41, 17455): 1118.1586708941472, (41, 17491): 1126.6813671729028, (41, 17507): 1065.1395738771166, (41, 17509): 1065.1705471618072, (41, 17590): 1098.6705889426637, (41, 17615): 1012.851852552425, (41, 17642): 1021.136538752435, (41, 17643): 1025.187405677157, (41, 17668): 1010.0451009398575, (41, 17721): 979.4538285722722, (41, 17754): 997.6460240449724, (41, 17769): 1053.4993316660461, (41, 17776): 1062.7173302878646, (41, 17804): 1056.0412118188383, (41, 17809): 1058.8057143132808, (41, 17824): 1049.9963121263431, (41, 17837): 1074.7162104531737, (41, 17838): 1081.1855108551601, (41, 17862): 1082.1305547875074, (41, 17866): 1084.9535499272185, (41, 17872): 1076.4709304379169, (41, 17873): 1075.7941560804873, (41, 17881): 1077.77279624117, (41, 17947): 1825.8777531368899, (41, 17951): 1819.0115948501282, (41, 17953): 1815.6676425107114, (41, 17954): 1814.8151813558966, (41, 17959): 1827.9576857334998, (41, 17963): 1829.0654494462203, (41, 18000): 1788.5848273097727, (41, 18001): 1787.2517539154828, (41, 18111): 1808.459539085518, (41, 18148): 1589.527456417891, (41, 18166): 1660.9511866962732, (41, 18189): 1753.3583737153085, (41, 18239): 1107.5032689998554, (41, 18240): 1108.6749163078148, (41, 18245): 1108.391169317682, (41, 18247): 1109.056481467121, (41, 18251): 1109.8469903251482, (41, 18256): 1112.1075889297213, (41, 18258): 1112.0923449522413, (41, 18259): 1112.8683237815578, (41, 18260): 1114.0501837866857, (41, 18262): 1115.4112681372058, (41, 18263): 1112.9795505261711, (41, 18264): 1114.0787617202425, (41, 18266): 1116.6923137362312, (41, 18267): 1117.5975031418197, (41, 18268): 1118.4911502313043, (41, 18269): 1120.4226428724494, (41, 18275): 1119.5168376354172, (41, 18285): 1113.2303677618702, (41, 18308): 1092.9515495446897, (41, 18313): 1089.4926734549645, (41, 18314): 1094.8488991186784, (41, 18315): 1117.0031092577235, (41, 18316): 1118.4919403573183, (41, 18317): 1119.4970590702196, (41, 18320): 1118.1141530837851, (41, 18321): 1119.392971425968, (41, 18322): 1120.6500835919228, (41, 18324): 1119.3811426001218, (41, 18325): 1121.061025930711, (41, 18326): 1120.3607957611357, (41, 18327): 1121.760820167169, (41, 18329): 1120.0208043806163, (41, 18330): 1124.1785877429866, (41, 18331): 1122.265059244137, (41, 18332): 1121.1245081775364, (41, 18333): 1122.57550364762, (41, 18336): 1119.2290727923698, (41, 18337): 1118.7730245213465, (41, 18403): 1126.9450896345413, (41, 18432): 1150.5568534832294, (41, 18451): 1134.8554796328845, (41, 18466): 1114.918620415341, (41, 18481): 1113.1694409422278, (41, 18483): 1114.3092378101635, (41, 18484): 1112.5124650428875, (41, 18485): 1105.9417722721546, (41, 18486): 1104.3176251999348, (41, 18487): 1100.7774640097743, (41, 18489): 1107.9539674981813, (41, 18490): 1106.981489871957, (41, 18491): 1107.991872686572, (41, 18492): 1099.5964441324068, (41, 18493): 1102.5845768586503, (41, 18494): 1108.4735251666727, (41, 18495): 1106.0568242258053, (41, 18496): 1105.9438907382225, (41, 18497): 1098.8947342918239, (41, 18498): 1104.0793874481403, (41, 18499): 1106.0796774783175, (41, 18501): 1102.5962288666137, (41, 18502): 1101.1839940265768, (41, 18503): 1101.5059270938402, (41, 18504): 1107.7793522851891, (41, 18506): 1099.469007642241, (41, 18507): 1097.4627444556122, (41, 18508): 1104.683906105048, (41, 18509): 1103.616232946996, (41, 18510): 1099.925692086518, (41, 18511): 1100.6134637525608, (41, 18512): 1101.3049151229536, (41, 18515): 1106.2657563460787, (41, 18516): 1102.5750416185515, (41, 18517): 1099.1323327178866, (41, 18518): 1104.6359771831242, (41, 18519): 1108.7158706390985, (41, 18520): 1105.685140575123, (41, 18522): 1116.2501536609388, (41, 18523): 1115.2459718590044, (41, 18532): 1115.087109332601, (41, 18535): 1114.13309022469, (41, 18537): 1113.6057638885823, (41, 18539): 1113.061362371956, (41, 18540): 1112.4303747766714, (41, 18541): 1112.117367498775, (41, 18542): 1112.038331394156, (41, 18543): 1111.9205595404137, (41, 18546): 1109.8440443882446, (41, 18555): 1110.5546549957903, (41, 18556): 1109.828190078068, (41, 18565): 1113.335699313251, (41, 18567): 1111.0804296798203, (41, 18568): 1111.7428204565053, (41, 18577): 1115.1554422307045, (41, 18583): 1118.032514052767, (41, 18605): 1122.9094061703884, (41, 18608): 1106.3250959774903, (41, 18616): 1125.9658797856625, (41, 18618): 1126.4416254323821, (41, 18625): 1134.6873570115583, (41, 18645): 1135.9952919130174, (41, 18646): 1133.6201202957945, (41, 18653): 1122.5913850639627, (41, 18654): 1124.3958939504619, (41, 18655): 1121.31782723593, (41, 18666): 1145.884790768643, (41, 18837): 1264.8744456425075, (41, 18974): 1163.2253583986544, (41, 18999): 1180.5627176635264, (41, 19000): 1181.7418501595516, (41, 19174): 1213.4308224383278, (41, 19342): 1256.6712814621274, (41, 19455): 1161.959137298819, (41, 19555): 1168.2433335299618, (41, 19564): 1204.2159152024565, (41, 19573): 1195.6334572457333, (41, 19586): 1189.5891542930115, (41, 19605): 1184.5657113040156, (41, 19611): 1189.0518834908144, (41, 19614): 1177.648270726279, (41, 19641): 1212.989409329118, (41, 19702): 1223.0960497599683, (41, 19713): 1218.137297948969, (41, 19731): 1113.0487815712127, (41, 19819): 1177.5390078105804, (41, 19893): 624.8696666506418, (41, 19899): 588.9018457073597, (41, 19929): 623.3905916045386, (41, 19951): 583.7856838924446, (41, 19962): 604.513427411379, (41, 19970): 626.8047177574983, (41, 19971): 619.3287754483225, (41, 19972): 617.4167743625029, (41, 19975): 624.1247215157936, (41, 19978): 610.0995177152134, (41, 19987): 614.5414910742082, (41, 19989): 623.4437517341831, (41, 20039): 615.3974795381913, (41, 20043): 618.8360567133166, (41, 20047): 627.5611418983743, (41, 20052): 631.5386699549776, (41, 20054): 627.5136449063986, (41, 20085): 637.7830208381932, (41, 20104): 637.6778222401806, (41, 20132): 632.3346679406995, (41, 20203): 561.5075360612377, (41, 20280): 545.6102078424029, (41, 20285): 538.2017734361963, (41, 20290): 547.5622635666208, (41, 20297): 553.2005211628193, (41, 20309): 555.6264631552253, (41, 20453): 575.7559197859988, (41, 20485): 587.5918062628973, (41, 20520): 603.5988377268892, (41, 20526): 587.2698290646406, (41, 20698): 1786.1678678302953, (41, 20868): 1934.0407478921863, (41, 21042): 943.6207941219047, (41, 21057): 945.7251280912153, (41, 21066): 935.2959214669995, (41, 21075): 948.1068868637898, (41, 21093): 931.0819254030168, (41, 21098): 913.4734031045857, (41, 21127): 936.9880952886683, (41, 21130): 930.9693927157645, (41, 21144): 942.8788852344943, (41, 21146): 937.0091618712501, (41, 21147): 946.435727106297, (41, 21148): 942.4418185202761, (41, 21153): 988.4768662676017, (41, 21293): 930.7268191914682, (41, 21426): 1046.392645553568, (41, 21442): 1073.900486106578, (41, 21451): 1076.147357506038, (41, 21466): 1053.618690713023, (41, 21469): 1052.0232024731988, (41, 21471): 1054.69323912738, (41, 21473): 1051.9480579232, (41, 21475): 1052.8475317484115, (41, 21482): 1055.7297880536578, (41, 21484): 1053.5785994971714, (41, 21488): 1055.7739564668768, (41, 21494): 1046.3511980158726, (41, 21498): 1046.7978938653455, (41, 21500): 1040.9673935336184, (41, 21514): 1016.3503665382624, (41, 21537): 1026.5223124741565, (41, 21662): 999.008523639694, (41, 21691): 1000.0551219440524, (41, 21757): 1051.890967331402, (41, 21777): 910.0632443632317, (41, 21778): 911.8696432504867, (41, 21779): 905.1691526361353, (41, 21790): 914.2797856435955, (41, 21802): 903.1738656984247, (41, 21824): 895.687270694445, (41, 21874): 897.7166157592952, (41, 21879): 888.4146048282904, (41, 21983): 939.1326213968164, (41, 22002): 885.4647248776921, (41, 22132): 1029.6770125203898, (41, 22261): 1261.8018498361273, (41, 22298): 1242.4976766565874, (41, 22339): 1282.6820771737973, (41, 22508): 1165.0599592443123, (41, 22841): 2988.237328109306, (41, 22842): 2987.327233202116, (41, 22874): 2968.3977806432285, (41, 22941): 2973.2211525891958, (41, 22956): 2981.9913504614246, (41, 22960): 2987.0788541048796, (41, 22968): 2983.4892300667752, (41, 22970): 2988.017089193215, (41, 22974): 2984.369889385929, (41, 22980): 2995.766462700147, (41, 23025): 2982.3130583565517, (41, 23028): 2977.1929756818436, (41, 23081): 2980.6126486808384, (41, 23104): 2937.8257706204045, (41, 23147): 2874.1106354866565, (41, 23298): 986.6922147794593, (41, 23376): 982.3918004129614, (41, 23381): 950.8087720034657, (41, 23529): 965.5417302173743, (41, 23556): 966.6981919024381, (41, 23718): 1008.2833563006438, (41, 24001): 1025.8139453360682, (41, 24094): 988.234161975028, (41, 24129): 995.4457730260066, (41, 24174): 960.7398472805542, (41, 24235): 962.8368906822797, (41, 24259): 983.294972365365, (41, 24260): 980.7223628063152, (41, 24261): 981.0144851219334, (41, 24305): 997.7651409471615, (41, 24306): 996.6193783756011, (41, 24307): 995.8571382995995, (41, 24308): 1076.1788371346604, (41, 24498): 1058.6248018125234, (41, 24499): 1057.869116527365, (41, 24500): 1057.2879508640083, (41, 24668): 1096.827444959251, (41, 24711): 1047.8660367606283, (41, 24756): 1036.1827686784438, (41, 24788): 1046.184362416301, (41, 24809): 1018.6061029790832, (41, 24813): 1028.682216176059, (41, 24821): 1026.0526158040734, (41, 24825): 1025.053231569667, (41, 24832): 1019.1049913775313, (41, 24833): 1021.5952354968524, (41, 24835): 1023.1899716507567, (41, 24837): 1029.2743579297808, (41, 24840): 1017.6416334480813, (41, 24841): 1023.7228387702297, (41, 24844): 1016.2935173989163, (41, 24845): 1024.2631502748045, (41, 24846): 1016.0199207549408, (41, 24849): 1016.6792906593405, (41, 24850): 1027.6695855595397, (41, 24863): 1004.1504198290947, (41, 24866): 1008.9771375436956, (41, 24885): 1009.2260674274743, (41, 24886): 1006.4306760146568, (41, 24889): 1027.4154633624628, (41, 24903): 1036.13988162099, (41, 24909): 1027.75258533869, (41, 24999): 1271.1625011676176, (41, 25019): 1276.2453524171788, (41, 25028): 1265.5805645886135, (41, 25137): 453.3201357803299, (41, 25145): 453.006806202127, (41, 25208): 377.124299994334, (41, 25233): 373.6510420341423, (41, 25371): 504.21929586928763, (41, 25377): 520.9767833848655, (41, 25828): 709.9355058788683, (41, 25851): 773.253806544251, (41, 25874): 728.2182013938027, (41, 25898): 688.0725871279393, (41, 25946): 715.424663472528, (41, 26047): 589.1336379667721, (41, 26066): 657.3167461860701, (41, 26197): 625.3957518498496, (41, 26212): 790.3446117874862, (41, 26253): 801.4642069779343, (41, 26254): 798.6042333768875, (41, 26257): 790.0948667806207, (41, 26258): 797.8694876544151, (41, 26260): 794.2054765261901, (41, 26266): 809.0450784348202, (41, 26267): 803.1250525047761, (41, 26271): 801.6512440727456, (41, 26304): 771.4108892569063, (41, 26305): 775.684685256204, (41, 26363): 696.1798844485794, (41, 26441): 1143.2477850732676, (41, 26442): 1143.8415270802489, (41, 26450): 1135.0415347296791, (41, 26459): 1124.7081215478906, (41, 26462): 1121.663469905367, (41, 26467): 1145.9911590550826, (41, 26471): 1143.9800956006081, (41, 26472): 1144.675410910317, (41, 26473): 1145.7675592560988, (41, 26476): 1156.0485344234805, (41, 26485): 1133.6081118661923, (41, 26493): 1138.8282606873474, (41, 26524): 1120.9918975197918, (41, 26525): 1122.6759868597053, (41, 26556): 1140.2196346417538, (41, 26560): 1131.4014474544306, (41, 26561): 1124.2780212871717, (41, 26564): 1140.1643763748655, (41, 26569): 1125.6473108562377, (41, 26570): 1126.6247641733628, (41, 26573): 1132.2548922226513, (41, 26581): 1135.8914551510034, (41, 26583): 1131.7097056463087, (41, 26593): 1140.7982475574804, (41, 26837): 1151.5255987254302, (41, 26844): 1155.3628459294143, (41, 26863): 1156.376245030672, (41, 26893): 1171.1778035681928, (41, 26902): 1176.7657412398823, (41, 26905): 1162.8090230233122, (41, 26912): 1169.8100273140146, (41, 26921): 1162.8673723927209, (41, 26922): 1165.2782540047372, (41, 27212): 1000.20145729562, (41, 27218): 986.3106414861613, (41, 27239): 1011.7961913059606, (41, 27257): 1009.2914814689249, (41, 27274): 1015.3487375133811, (41, 27279): 1017.1947618902766, (41, 27282): 1011.1455367747202, (41, 27283): 1007.7883208269276, (41, 27285): 1019.8680396787197, (41, 27286): 1019.4610372491485, (41, 27290): 1006.4892383693136, (41, 27295): 998.3593902251936, (41, 27300): 1015.2347255002171, (41, 27344): 1012.4860383187412, (41, 27366): 1022.1643909509156, (41, 27383): 1026.5768988018215, (41, 27398): 1026.8495202474228, (41, 27406): 1018.6233906313777, (41, 27407): 1018.0772966266314, (41, 27426): 990.1941720320198, (41, 27432): 970.1859082961386, (41, 27460): 979.9113242393161, (41, 27523): 1070.8556415838964, (41, 27545): 1129.7343174440316, (41, 27602): 1304.2065716208886, (41, 27606): 1304.0170700396634, (41, 27646): 1191.8169119409174, (41, 27667): 1223.6781219621116, (41, 27672): 1223.240781605497, (41, 27674): 1219.0888431069393, (41, 27688): 1215.3158865148546, (41, 27692): 1231.228129156612, (41, 27693): 1226.85728614599, (41, 27705): 1229.0180426555112, (41, 27712): 1233.2006736064316, (41, 27786): 1233.4819339170745, (41, 27790): 1187.922235433737, (41, 27791): 1182.494128115274, (41, 27795): 1226.2834349178247, (41, 27801): 1194.72638603175, (41, 27813): 1241.742413625979, (41, 27816): 1230.2723801791865, (41, 27823): 1193.291231319077, (41, 27830): 1216.68187807903, (41, 27884): 1165.327474449452, (41, 27885): 1182.4187590264062, (41, 27896): 1170.579181580827, (41, 27919): 1167.4074017195505, (41, 27922): 1173.0877729337683, (41, 27930): 1164.7197597162258, (41, 27934): 1167.5155817948785, (41, 27935): 1170.454852402235, (41, 27948): 1391.3671403312917, (41, 27951): 1365.8460614562623, (41, 28061): 1515.1874839056725, (41, 28290): 1773.594484474365, (41, 28292): 1788.4280136359591, (41, 28293): 1777.16253353932, (41, 28295): 1779.8925939117144, (41, 28296): 1776.1559799004906, (41, 28297): 1766.301667123622, (41, 28302): 1768.92598867616, (41, 28310): 2261.566975229451, (41, 28313): 2275.5491161731907, (41, 28372): 2260.292240678164, (41, 28398): 2262.091352366206, (41, 28399): 2260.7992885130047, (41, 28400): 2265.031345931373, (41, 28401): 2251.865864953009, (41, 28445): 2276.9153270093316, (41, 28475): 2231.7896341240807, (41, 28885): 884.012790009763, (41, 28886): 879.6230815714493, (41, 28915): 867.1923424086874, (41, 28916): 870.5699502883346, (41, 28917): 867.1050833361172, (41, 28921): 888.956304374506, (41, 28931): 885.1150095669507, (41, 28945): 834.746343193244, (41, 28982): 850.9664928104362, (41, 29219): 783.5116929500487, (41, 29228): 782.9415216004525, (41, 29246): 755.4941864275393, (41, 29248): 741.2497420470322, (41, 29282): 743.0013826570213, (41, 29290): 770.8958164233322, (41, 29291): 766.6109868997936, (41, 29292): 768.6192268811593, (41, 29293): 768.3773340521338, (41, 29294): 762.637018324046, (41, 29298): 764.7035575721704, (41, 29299): 760.9369555715183, (41, 29304): 769.0616702053889, (41, 29317): 773.9088950976062, (41, 29323): 774.7267263443182, (41, 29330): 771.66582448316, (41, 29331): 773.3112509325958, (41, 29344): 755.5021541747562, (41, 29445): 710.8142936204916, (41, 29724): 2995.079331908994, (41, 29738): 2998.076286500205, (41, 29745): 2990.5301196583027, (41, 29748): 2998.2832406558205, (41, 29750): 3005.706258609577, (41, 29759): 2993.4322165584176, (41, 29772): 3004.6246581139085, (41, 29781): 3002.353315763666, (41, 29784): 2997.8577785929133, (41, 29790): 3005.845230903732, (41, 29811): 3002.117056173956, (41, 29817): 3038.0945466984135, (41, 29818): 3035.9668390691713, (41, 29929): 2985.686209771708, (41, 30039): 3007.3462114121558, (41, 30066): 2971.859806484857, (41, 30116): 2883.897485948973, (41, 30238): 2751.125802337437, (41, 30248): 2799.007382511662, (41, 30260): 2798.899942796476, (41, 30545): 918.7614733440264, (41, 30733): 940.3330357350693, (41, 30756): 873.579412273192, (41, 30921): 894.6633745939494, (41, 31079): 1306.0312474971884, (41, 31149): 1255.3059420895097, (41, 31154): 1263.9961030719644, (41, 31160): 1254.228346621787, (41, 31163): 1264.0624174561783, (41, 31189): 1249.888356817229, (41, 31215): 1258.4760310431773, (41, 31259): 1297.2138812954988, (41, 31262): 1293.7998587408174, (41, 31430): 1332.7064756737414, (41, 31568): 1399.0040408752454, (41, 31751): 1323.8321142313644, (42, 109): 908.4242632446291, (42, 872): 2442.691857363199, (42, 873): 2450.886093409726, (42, 877): 2447.8667012697906, (42, 879): 2449.0874898221437, (42, 884): 2440.9748897810355, (42, 889): 2446.084849451566, (42, 891): 2438.2495570396063, (42, 892): 2455.428062126672, (42, 894): 2454.371444010018, (42, 896): 2446.3846242229415, (42, 903): 2448.235756200223, (42, 909): 2434.1036205660316, (42, 910): 2437.3331837985743, (42, 912): 2431.9246782693317, (42, 913): 2425.984559743801, (42, 916): 2423.393243796151, (42, 926): 2439.9522630972015, (42, 927): 2437.1881377391055, (42, 948): 2435.2709832871674, (42, 961): 2439.781106391169, (42, 962): 2440.6752059554574, (42, 963): 2441.6916221046386, (42, 967): 2451.6782925644175, (42, 974): 2447.4049330201256, (42, 998): 2454.964001170188, (42, 1014): 2633.355236755369, (42, 1086): 2420.567526040749, (42, 1087): 2419.207859551042, (42, 1089): 2411.7956239027803, (42, 1090): 2415.287328199101, (42, 1092): 2427.135527109776, (42, 1097): 2418.162160657384, (42, 1107): 2432.827723715948, (42, 1387): 1177.4176579330901, (42, 1554): 1050.2079640061945, (42, 1827): 2816.4078778413423, (42, 1828): 2817.291633782906, (42, 1829): 2818.5342234327277, (42, 1830): 2817.160909714605, (42, 1831): 2817.908239582782, (42, 1832): 2817.03651985265, (42, 1833): 2817.1489083354627, (42, 1836): 2816.222111794189, (42, 1841): 2821.4380435905764, (42, 1843): 2819.244403929594, (42, 1844): 2820.2073185196423, (42, 1845): 2817.583411554606, (42, 1847): 2809.1685751457267, (42, 1848): 2812.0752689814235, (42, 1849): 2825.6824412550004, (42, 1850): 2827.1218652832877, (42, 1851): 2814.263359201515, (42, 1852): 2814.4440843913876, (42, 1854): 2815.861421770088, (42, 1856): 2808.714530834593, (42, 1857): 2811.8599471440234, (42, 1858): 2824.3806605815275, (42, 1861): 2818.324478017722, (42, 1866): 2808.501687783734, (42, 1867): 2821.6156355886005, (42, 1868): 2819.879213643077, (42, 1870): 2819.9240191367144, (42, 1871): 2821.243289855619, (42, 1875): 2815.735366942045, (42, 1880): 2810.5633078896026, (42, 1882): 2811.3781653651654, (42, 1883): 2827.2708196219473, (42, 1889): 2812.1335946898107, (42, 1893): 2818.7401921115315, (42, 1894): 2816.6887389126728, (42, 1899): 2810.3373213869722, (42, 1900): 2811.8643378944407, (42, 1902): 2822.3130034647606, (42, 1905): 2824.9501281599373, (42, 1907): 2814.0852954189713, (42, 1910): 2815.1001565592555, (42, 1917): 2830.630629259547, (42, 1920): 2814.309806341832, (42, 1935): 2825.366926794261, (42, 1937): 2827.621330031642, (42, 1946): 2805.819765165788, (42, 1949): 2808.3655041179, (42, 1950): 2799.407101557877, (42, 1951): 2803.7171962444263, (42, 1952): 2806.8670059336214, (42, 1953): 2808.3228612085272, (42, 1954): 2806.256991550427, (42, 1958): 2807.6206304803745, (42, 1960): 2811.9103952160117, (42, 1968): 2813.6031854661946, (42, 1969): 2825.9334826690038, (42, 1974): 2822.705625781291, (42, 1975): 2822.65816196993, (42, 1979): 2816.566763418062, (42, 1980): 2816.05044066764, (42, 1981): 2817.8608686510615, (42, 1985): 2819.343083346492, (42, 1994): 2795.8524312667005, (42, 2011): 2811.2538543325672, (42, 2019): 2832.5309802335482, (42, 2020): 2829.717659204961, (42, 2029): 2818.986617955713, (42, 2030): 2827.7683295521183, (42, 2032): 2817.206684962746, (42, 2033): 2822.931875418458, (42, 2034): 2822.8081131078197, (42, 2036): 2811.976969649688, (42, 2037): 2814.754455963125, (42, 2038): 2815.797921288591, (42, 2042): 2848.3122784582415, (42, 2050): 2821.5023397486934, (42, 2051): 2821.0075023458535, (42, 2053): 2821.881998661793, (42, 2054): 2824.758265589129, (42, 2066): 2818.9004661876907, (42, 2067): 2818.9321330423877, (42, 2071): 2790.4336425931197, (42, 2072): 2795.8424551516837, (42, 2073): 2781.070019646673, (42, 2074): 2780.3304027098807, (42, 2080): 2771.1918975690146, (42, 2082): 2798.7553817850935, (42, 2083): 2801.553214799154, (42, 2089): 2795.6393822318314, (42, 2090): 2798.2511993761236, (42, 2092): 2794.704171527888, (42, 2098): 2774.694436697634, (42, 2099): 2777.8336463428236, (42, 2101): 2774.1196849299895, (42, 2102): 2788.860003014744, (42, 2103): 2784.2227095315507, (42, 2104): 2781.683365887838, (42, 2106): 2803.4338688296316, (42, 2112): 2776.073706340642, (42, 2113): 2790.954571731974, (42, 2114): 2794.4963881131953, (42, 2117): 2805.6384616644405, (42, 2123): 2783.7141797885533, (42, 2124): 2786.75207456214, (42, 2134): 2778.181375614117, (42, 2138): 2787.086622751049, (42, 2141): 2779.208413230911, (42, 2148): 2783.939337884149, (42, 2150): 2771.8299679523075, (42, 2151): 2775.051138862954, (42, 2152): 2770.172138977841, (42, 2153): 2784.9414878551597, (42, 2154): 2772.3368970925767, (42, 2155): 2770.9295895725127, (42, 2156): 2768.5574768284278, (42, 2157): 2771.8904539783807, (42, 2160): 2791.4856591967123, (42, 2161): 2769.67943645669, (42, 2162): 2785.560352242862, (42, 2163): 2781.2844680459134, (42, 2164): 2781.0120491132584, (42, 2168): 2773.2151120393, (42, 2172): 2776.174260858618, (42, 2174): 2774.723516256177, (42, 2178): 2778.699814712262, (42, 2179): 2776.7433063147423, (42, 2183): 2786.917522083554, (42, 2185): 2787.129139918843, (42, 2186): 2784.6933841935934, (42, 2190): 2792.0479399651686, (42, 2192): 2787.6695285459496, (42, 2193): 2787.7577575227238, (42, 2194): 2783.284820661092, (42, 2195): 2782.6819384071473, (42, 2197): 2788.648576749045, (42, 2205): 2782.4479927876305, (42, 2207): 2774.3645163915407, (42, 2208): 2778.8936450565693, (42, 2212): 2788.963413897667, (42, 2214): 2699.3793377383863, (42, 2225): 2710.1483312824403, (42, 2231): 2688.26518378272, (42, 2278): 2754.6456480777033, (42, 2284): 2763.8318946599647, (42, 2285): 2762.54862447682, (42, 2291): 2744.3042662635144, (42, 2292): 2746.306929053654, (42, 2307): 2757.863489286121, (42, 2313): 2742.1346024739028, (42, 2317): 2739.5183273424386, (42, 2319): 2749.46623718321, (42, 2321): 2753.6809157162284, (42, 2323): 2753.1277390866385, (42, 2326): 2769.1849487137633, (42, 2327): 2765.208923630897, (42, 2329): 2762.4953459486374, (42, 2330): 2759.4045260980733, (42, 2332): 2765.9547561161257, (42, 2344): 2755.812337673715, (42, 2346): 2755.629285378112, (42, 2361): 2754.0155875990154, (42, 2368): 2800.454988621222, (42, 2374): 2804.8346027573275, (42, 2375): 2806.297159613869, (42, 2377): 2791.012505262405, (42, 2378): 2809.05533997552, (42, 2379): 2809.4416334606976, (42, 2380): 2810.95005361214, (42, 2383): 2795.0861654178957, (42, 2385): 2797.443796087695, (42, 2395): 2797.7002891280245, (42, 2397): 2807.6248536934363, (42, 2398): 2786.143137351586, (42, 2399): 2791.6393862505506, (42, 2400): 2790.4061759570836, (42, 2402): 2799.142020455423, (42, 2403): 2802.557226852657, (42, 2404): 2803.4376485288017, (42, 2405): 2795.2065008602667, (42, 2407): 2801.9123581001286, (42, 2408): 2805.920107327813, (42, 2409): 2797.703460427466, (42, 2411): 2802.5257139917, (42, 2412): 2801.6327380555776, (42, 2413): 2804.433183704948, (42, 2414): 2799.877375728994, (42, 2422): 2801.482292157034, (42, 2424): 2802.5983150457364, (42, 2426): 2803.339575125731, (42, 2433): 2796.9710252504997, (42, 2436): 2795.2716562254827, (42, 2437): 2775.3327566926164, (42, 2440): 2779.7286873007893, (42, 2445): 2867.7015612543355, (42, 2447): 2856.90170949022, (42, 2454): 2867.0995804630543, (42, 2455): 2867.694819815475, (42, 2460): 2835.9889840488, (42, 2461): 2839.8963688442122, (42, 2471): 2902.8796844811927, (42, 2492): 2833.502129641358, (42, 2511): 2802.3891086733274, (42, 2523): 2818.2980332653437, (42, 2525): 2813.348183978221, (42, 2535): 2823.1595960492887, (42, 2537): 2816.1190838199554, (42, 2538): 2821.049194735608, (42, 2539): 2818.6368664274646, (42, 2540): 2826.3444463865576, (42, 2542): 2831.3151085138106, (42, 2559): 2931.6732705867475, (42, 2575): 2922.239796053465, (42, 2599): 2772.277082747118, (42, 2600): 2805.869914242119, (42, 2607): 2786.6764775773, (42, 2627): 2820.1664796594064, (42, 2647): 2838.296044577628, (42, 2674): 2829.3790484862684, (42, 2681): 2826.5241860531855, (42, 2683): 2835.6829195361092, (42, 2686): 2825.4498691171457, (42, 2689): 2945.653767892923, (42, 2690): 2946.1678041016726, (42, 2713): 2967.226015021511, (42, 2714): 2968.9346221681276, (42, 2715): 2971.912891535768, (42, 2739): 2969.364870574104, (42, 2740): 2951.441136780033, (42, 2741): 2952.982159772923, (42, 2749): 2964.916570381731, (42, 2750): 2965.961093109988, (42, 2752): 2968.1360712096675, (42, 2755): 2970.4195036223414, (42, 2758): 2969.6367796175487, (42, 2759): 2969.6980815263614, (42, 2769): 2966.367809413541, (42, 2771): 2956.0281551431885, (42, 2779): 2956.155586132225, (42, 2784): 2922.285137272141, (42, 2800): 2927.4546993971476, (42, 2802): 2945.259634664014, (42, 2803): 2944.2244724593943, (42, 2804): 2942.273418162223, (42, 2805): 2947.470633308372, (42, 2807): 2947.384731202732, (42, 2809): 2946.052852662247, (42, 2812): 2927.1989250111437, (42, 2814): 2944.371235363509, (42, 2817): 2944.081674022225, (42, 2819): 2948.015615493204, (42, 2823): 2928.180551434873, (42, 2832): 2951.0278393579174, (42, 2836): 2937.6333286925474, (42, 2839): 2947.442675238054, (42, 2841): 2945.227711606844, (42, 2843): 2944.4010915264134, (42, 2846): 2939.866526561654, (42, 2849): 2952.946737482322, (42, 2852): 2949.969944429462, (42, 2853): 2954.3105380257184, (42, 2876): 2955.1842305761265, (42, 2877): 2965.8564241117256, (42, 2885): 2968.087686642077, (42, 2918): 2950.1481163434883, (42, 2921): 2954.659670974154, (42, 2925): 2933.755136598289, (42, 2926): 2926.913481497204, (42, 2930): 2941.8502540408626, (42, 2931): 2935.513262803709, (42, 2938): 2950.045083336898, (42, 2940): 2964.217088141167, (42, 2947): 2948.6164143245646, (42, 2949): 2942.078564415079, (42, 2950): 2943.9997064215836, (42, 2952): 2941.713363500572, (42, 2958): 2941.3333641508525, (42, 2959): 2943.7135061671893, (42, 2960): 2948.735928380086, (42, 2961): 2946.2241980574895, (42, 2963): 2939.3092355154395, (42, 2968): 2940.667234393923, (42, 2976): 2938.7975907346918, (42, 2981): 2894.222568084195, (42, 2982): 2892.7746353710254, (42, 2984): 2890.4698478644914, (42, 3003): 2886.2814714861015, (42, 3046): 2858.805837601494, (42, 3050): 2881.094627874339, (42, 3051): 2882.951845721857, (42, 3053): 2877.88806547899, (42, 3069): 2905.452314480562, (42, 3071): 2877.0971777875557, (42, 3080): 2967.785395862264, (42, 3199): 2877.6740378467566, (42, 3200): 2872.2667394197547, (42, 3205): 2904.862106880531, (42, 3209): 2874.9969796036994, (42, 3215): 2872.703382742499, (42, 3217): 2866.1854517111733, (42, 3249): 2873.4118132721537, (42, 3263): 2922.6733440539583, (42, 3289): 2889.2615857424057, (42, 3301): 2890.5487247385095, (42, 3302): 2888.303023951981, (42, 3307): 2885.406277221709, (42, 3310): 2893.3540268677652, (42, 3391): 2893.2316091592215, (42, 3509): 1847.0434984590083, (42, 3510): 1842.4112378404834, (42, 3511): 1845.6269573149375, (42, 3512): 1842.8751516136203, (42, 3514): 1843.9510972504543, (42, 3519): 1857.2618968455477, (42, 3536): 1855.4448719477066, (42, 3545): 1862.8443734345133, (42, 3548): 1855.9078228514986, (42, 3572): 1857.9179739640585, (42, 3581): 1851.867865821434, (42, 3583): 1849.253380016659, (42, 3601): 1865.7550468250245, (42, 3656): 1857.7177157085903, (42, 3669): 1847.5160352515102, (42, 3670): 1851.6215809920677, (42, 3695): 1828.3674113046773, (42, 3696): 1831.6699946461194, (42, 3782): 1859.6644695344892, (42, 3792): 1854.2725753800448, (42, 3989): 197.85715062387703, (42, 4008): 221.43299940305488, (42, 4031): 231.25290995455185, (42, 4045): 211.99777880021688, (42, 4144): 203.02225442073885, (42, 4145): 167.95934397166928, (42, 4164): 191.12972044315626, (42, 4168): 178.54711167242635, (42, 4173): 174.5374175375581, (42, 4181): 159.76776141698173, (42, 4228): 158.6115384234257, (42, 4248): 135.8628145927356, (42, 4254): 44.91235790259283, (42, 4260): 39.35741168078717, (42, 4262): 34.134776869023696, (42, 4273): 32.50169114883589, (42, 4319): 141.90538785660814, (42, 4326): 143.42585507939663, (42, 4328): 140.8685838001795, (42, 4334): 139.93111600202164, (42, 4335): 142.9501561731827, (42, 4372): 908.7690972115787, (42, 4413): 955.2683311726488, (42, 4434): 902.1461502439787, (42, 4447): 887.9574821475965, (42, 4452): 905.1837783540254, (42, 4463): 981.240208729835, (42, 4465): 975.3024919543052, (42, 4619): 1012.8326324418924, (42, 4645): 1005.9411410086901, (42, 4657): 1012.4931196907921, (42, 4666): 1017.9639673841552, (42, 4676): 1018.8938629683006, (42, 4678): 1015.9036085855382, (42, 4689): 1023.2915912966424, (42, 4704): 1030.756918278872, (42, 4726): 1202.2625175183873, (42, 4727): 1199.6251632268945, (42, 4730): 1194.0799734231543, (42, 4731): 1198.5624138551505, (42, 4734): 1184.8903347418686, (42, 4735): 1184.8875903291976, (42, 4736): 1188.3123962745499, (42, 4737): 1186.8336965897047, (42, 4738): 1189.1732732146402, (42, 4756): 1193.1313497887277, (42, 4760): 1167.7525408695922, (42, 4761): 1164.3219175217137, (42, 4762): 1167.1590269439175, (42, 4765): 1170.5095816752157, (42, 4773): 1205.0502690018955, (42, 4774): 1206.6738351759445, (42, 4790): 1202.6984725797704, (42, 4795): 1199.3956632338372, (42, 4799): 1209.9200571456654, (42, 4801): 1220.8797286747053, (42, 4804): 1195.3067672559914, (42, 4805): 1192.6501594737422, (42, 4806): 1211.5353754266685, (42, 4815): 1212.5100715492324, (42, 4816): 1217.2979883552985, (42, 4817): 1223.1695296856867, (42, 4826): 1217.8368502225785, (42, 4830): 1216.0522088044556, (42, 4839): 1175.6127853973087, (42, 4840): 1179.9353516865247, (42, 4841): 1176.0223115569916, (42, 4846): 1173.4279614501052, (42, 4848): 1176.8249617141455, (42, 4850): 1179.8790668986253, (42, 4871): 1131.411722816272, (42, 4883): 1158.987611180423, (42, 4900): 1139.1312681301986, (42, 4901): 1139.1139026177657, (42, 4917): 1091.6871640715915, (42, 4931): 1080.5860828811785, (42, 4944): 1089.974278035126, (42, 4956): 1085.5844675835324, (42, 4958): 1091.1728288942602, (42, 4959): 1093.1407203116282, (42, 4961): 1085.4028102921109, (42, 4966): 1086.334036141224, (42, 5207): 1075.0836284083884, (42, 5272): 758.419261688482, (42, 5283): 760.6529457403209, (42, 5287): 778.2041340868676, (42, 5289): 779.823251261487, (42, 5293): 745.4376483498864, (42, 5295): 749.8473381213183, (42, 5296): 758.2311291690391, (42, 5298): 762.8696169229025, (42, 5303): 771.5782259122694, (42, 5305): 773.7257554619872, (42, 5306): 784.3500857915324, (42, 5307): 773.641651441518, (42, 5308): 777.1758045382765, (42, 5313): 766.5671968968902, (42, 5314): 764.4070703032089, (42, 5317): 782.6463564366488, (42, 5319): 771.8635536492811, (42, 5324): 764.4401637138075, (42, 5326): 759.2036591398687, (42, 5348): 791.17069797281, (42, 5351): 804.0539980769654, (42, 5399): 793.2347032602958, (42, 5413): 824.8288415674828, (42, 5422): 785.8566386916756, (42, 5445): 785.503042781446, (42, 5448): 784.067319896774, (42, 5456): 792.6272702650434, (42, 5467): 796.3414041130646, (42, 5624): 757.6020833609252, (42, 5671): 695.9541792368211, (42, 5672): 690.9271102187396, (42, 5797): 760.080534548456, (42, 5871): 905.5523800145685, (42, 5976): 881.3635001106767, (42, 6118): 2398.2410749217347, (42, 6248): 2494.569250600177, (42, 6345): 803.5232508559259, (42, 6352): 826.0234100568362, (42, 6354): 797.8413159056208, (42, 6359): 793.7523108509741, (42, 6376): 823.4924792841382, (42, 6378): 800.5393641689742, (42, 6381): 795.8423106738952, (42, 6383): 808.1448200031001, (42, 6396): 800.0838068017337, (42, 6399): 803.6910516365602, (42, 6408): 824.8208921292342, (42, 6409): 813.3912119668386, (42, 6419): 848.2490923802745, (42, 6422): 821.1510362660152, (42, 6423): 822.9104764041278, (42, 6424): 799.1286869134605, (42, 6439): 803.1736944278798, (42, 6464): 809.1235706058944, (42, 6465): 811.591372305985, (42, 6469): 809.3834390208791, (42, 6470): 810.9003962250804, (42, 6472): 786.2815758917646, (42, 6480): 789.5722094962429, (42, 6486): 775.4920182188689, (42, 6497): 780.082799879291, (42, 6503): 806.5389462440049, (42, 6508): 805.5092455584604, (42, 6509): 800.9766423090186, (42, 6521): 786.3160042520594, (42, 6544): 787.2866113444809, (42, 6552): 816.001174065443, (42, 6553): 819.3775156313434, (42, 6554): 822.8214861096401, (42, 6578): 810.4559365713941, (42, 6582): 812.3524304913302, (42, 6601): 808.7605431565021, (42, 6609): 782.2256196396136, (42, 6610): 781.0720857079341, (42, 6611): 780.8881224401408, (42, 6614): 782.9924860448644, (42, 6615): 782.1693656305512, (42, 6616): 777.9567787990478, (42, 6617): 779.7357970080857, (42, 6618): 774.1159177809792, (42, 6619): 785.3675584306209, (42, 6620): 777.6115721640263, (42, 6621): 780.466297275182, (42, 6622): 779.9689679140208, (42, 6623): 782.9379442530098, (42, 6624): 785.2057984757696, (42, 6625): 785.918168506069, (42, 6626): 785.6826235288815, (42, 6627): 784.0249586049144, (42, 6628): 777.9624783385499, (42, 6629): 784.0467985815349, (42, 6630): 788.9605437173905, (42, 6632): 784.4988551478455, (42, 6634): 791.8912153255218, (42, 6635): 781.6542623698427, (42, 6636): 777.6962554560677, (42, 6637): 788.0136001563425, (42, 6638): 788.278678899846, (42, 6639): 783.5109702527346, (42, 6640): 787.9579425468684, (42, 6641): 780.3475244610116, (42, 6642): 787.9961329243873, (42, 6643): 786.2713184528252, (42, 6645): 784.8058655705288, (42, 6646): 775.3652427188557, (42, 6647): 787.2352356698149, (42, 6653): 782.4059706582547, (42, 6655): 783.5946846694533, (42, 6658): 791.976773239619, (42, 6662): 787.9453137773577, (42, 6819): 951.3524522501272, (42, 6996): 896.2075051713532, (42, 7059): 857.8650649495994, (42, 7187): 942.3415758007162, (42, 7304): 1009.2404433687674, (42, 7528): 904.8754932368905, (42, 7720): 674.0523557750537, (42, 7793): 681.8553954230645, (42, 7807): 677.6511267431199, (42, 7808): 683.8293325673895, (42, 7831): 759.5550659404063, (42, 7850): 723.5703813261988, (42, 7852): 732.418154013751, (42, 8012): 681.9228726431567, (42, 8125): 684.5338823092203, (42, 8208): 605.569441712338, (42, 8392): 732.7215546178498, (42, 8651): 1137.3513647143977, (42, 9088): 970.5656123393661, (42, 9443): 1238.6116762712384, (42, 9444): 1233.7219426018523, (42, 9828): 1419.560937628363, (42, 9868): 1410.6619897326657, (42, 10180): 685.2313309805156, (42, 10256): 604.1389745532404, (42, 10276): 632.6293695777633, (42, 10378): 599.2297728655724, (42, 10676): 756.3471471510657, (42, 10714): 822.6164210541837, (42, 10730): 780.478234030568, (42, 10862): 1286.769037455937, (42, 10881): 1283.2051334618236, (42, 10883): 1285.9306427130923, (42, 10885): 1286.968728977701, (42, 10891): 1290.2235635233035, (42, 10909): 1284.9717516036656, (42, 10911): 1278.762679953074, (42, 10913): 1281.4290617075844, (42, 10915): 1278.5247241383793, (42, 10919): 1275.5545480401147, (42, 11037): 1370.595564647006, (42, 11039): 1357.2616841177464, (42, 11516): 552.4697457039816, (42, 11856): 138.37783651872576, (42, 11857): 149.31365004638494, (42, 11861): 143.91810781728557, (42, 11881): 136.4151726605561, (42, 11902): 149.14870303445434, (42, 11911): 145.11493015305408, (42, 11914): 145.95682614042494, (42, 11922): 138.5568868666917, (42, 11924): 133.7082020130067, (42, 11926): 136.9873879048979, (42, 11950): 121.98563628729147, (42, 11963): 111.08770104260527, (42, 11983): 107.58815217379805, (42, 11985): 106.86471744766753, (42, 12009): 97.58945034935273, (42, 12010): 108.29996313847434, (42, 12018): 105.59538440430207, (42, 12020): 104.7662258920837, (42, 12021): 102.28575847914516, (42, 12024): 94.73435671922677, (42, 12025): 99.4792856116978, (42, 12027): 100.65523065624525, (42, 12031): 109.77915320610012, (42, 12032): 108.55881597140599, (42, 12035): 95.78964319428154, (42, 12041): 113.57197828718822, (42, 12045): 229.50674661547458, (42, 12145): 159.76398765438918, (42, 12275): 232.56040891766742, (42, 12294): 235.70484932509436, (42, 12358): 296.9307264778548, (42, 12463): 333.32826797802903, (42, 12465): 333.4956166290326, (42, 12482): 331.5171671375357, (42, 12503): 333.0112623956303, (42, 12506): 335.5235330300769, (42, 12549): 316.3013784525603, (42, 12559): 317.0614368874924, (42, 12569): 324.03124297324257, (42, 12572): 325.6536691320935, (42, 12574): 320.75005250045723, (42, 12576): 316.9592336379936, (42, 12591): 308.95282091059704, (42, 12608): 320.8766226980301, (42, 12696): 288.84584382102815, (42, 12710): 295.8744004025257, (42, 12728): 297.50258715005356, (42, 12766): 507.2386718480417, (42, 12771): 517.0807561147153, (42, 12790): 521.4284290238331, (42, 12795): 533.4095610234776, (42, 12797): 560.6047276170169, (42, 12798): 555.0621235472829, (42, 12811): 526.9080783451329, (42, 12830): 539.0148137351262, (42, 12848): 528.662637298501, (42, 12850): 523.1420643475905, (42, 12852): 538.694671372898, (42, 12854): 543.0519285065849, (42, 12859): 522.9132012628372, (42, 12861): 549.0439091087243, (42, 12865): 524.1078929954722, (42, 12866): 524.6389376891993, (42, 12867): 517.5488862925542, (42, 12874): 521.2080115245263, (42, 12875): 517.2239725812974, (42, 12881): 532.528548724756, (42, 12883): 527.0050153928286, (42, 12885): 514.7940132543473, (42, 12888): 528.3663824464707, (42, 12889): 528.4952433741483, (42, 12892): 520.944325998016, (42, 12893): 529.3239875693275, (42, 12896): 525.5763008076739, (42, 12906): 526.2616111077944, (42, 13018): 598.7508868234207, (42, 13071): 606.8734018482533, (42, 13131): 610.249948654473, (42, 13146): 575.7154893255918, (42, 13159): 653.0568102823242, (42, 13193): 614.0177564612142, (42, 13198): 656.9090709884184, (42, 13292): 593.5178196418576, (42, 13296): 567.0165860247404, (42, 13406): 704.8886912687377, (42, 13407): 707.8952464100572, (42, 13417): 722.6053931895667, (42, 13418): 718.8995330123354, (42, 13438): 687.3306668429788, (42, 13442): 679.1492014864301, (42, 13443): 684.0200475137066, (42, 13764): 1150.7050310671495, (42, 13766): 1144.7325876346513, (42, 13771): 1154.7379472018029, (42, 13783): 1148.9147202130991, (42, 13784): 1136.4321428081607, (42, 13792): 1172.6275552081115, (42, 13824): 1153.826074629858, (42, 14017): 1096.3920342543104, (42, 14870): 1169.3704152043533, (42, 14997): 972.1534832021114, (42, 15000): 972.2398768646003, (42, 15003): 968.9690102478169, (42, 15006): 957.1034707411351, (42, 15007): 953.125252104854, (42, 15056): 955.6242252183989, (42, 15063): 959.6348259236788, (42, 15069): 961.8139059399147, (42, 15076): 952.9293618240403, (42, 15086): 964.8399990876093, (42, 15087): 970.0383357529328, (42, 15111): 981.5872610184184, (42, 15116): 975.0081393999737, (42, 15722): 1082.0593859348203, (42, 15998): 1173.969192323261, (42, 16073): 2032.671725691585, (42, 16939): 2556.608471810064, (42, 16940): 2550.6146880514943, (42, 16951): 2557.2510829676294, (42, 16963): 2557.8740851128164, (42, 16965): 2565.2503452564342, (42, 16969): 2563.361013196336, (42, 16970): 2560.5808542432906, (42, 16971): 2553.941616834796, (42, 16973): 2553.428808827607, (42, 16974): 2568.1512499551836, (42, 16976): 2561.137270382695, (42, 16978): 2556.309931515371, (42, 16980): 2563.6461110221717, (42, 16982): 2568.028849107318, (42, 17045): 2762.866464069798, (42, 17048): 2771.388038475074, (42, 17304): 88.07217837970009, (42, 17305): 93.12097508701122, (42, 17330): 93.38859793960353, (42, 17334): 80.32948990703223, (42, 17343): 99.65281318750793, (42, 17345): 88.9843375614845, (42, 17347): 98.73689104059835, (42, 17351): 72.27307452403332, (42, 17372): 82.9283472998558, (42, 17373): 98.01052339959544, (42, 17377): 99.76132730440362, (42, 17382): 91.75605412730681, (42, 17383): 90.34006242482386, (42, 17389): 86.34883128261754, (42, 17400): 93.13754023932171, (42, 17401): 91.68239545916367, (42, 17402): 94.41636129814707, (42, 17403): 95.90290881723894, (42, 17440): 99.72668160453105, (42, 17455): 103.96247597472134, (42, 17491): 111.38489570141428, (42, 17507): 58.24749362557141, (42, 17509): 61.89272671895878, (42, 17590): 80.7999271135138, (42, 17615): 17.517083661796814, (42, 17642): 18.944256903276624, (42, 17643): 17.759102636987993, (42, 17668): 19.51321070745767, (42, 17721): 42.62184636196515, (42, 17754): 68.31936427283947, (42, 17769): 54.85226809474865, (42, 17776): 46.72214416143073, (42, 17804): 62.92806740195254, (42, 17809): 68.2307466121455, (42, 17824): 63.725624264975465, (42, 17837): 62.34030890843773, (42, 17838): 67.32843070601521, (42, 17862): 66.66856239647693, (42, 17866): 73.22147824271691, (42, 17872): 60.823369763698125, (42, 17873): 58.09912554228647, (42, 17881): 63.49200223988727, (42, 17947): 2063.52264416291, (42, 17951): 2052.237627783665, (42, 17953): 2049.9684077329252, (42, 17954): 2050.683728714779, (42, 17959): 2061.398069532115, (42, 17963): 2057.6144537158625, (42, 18000): 1999.8741426117658, (42, 18001): 2001.9915038565055, (42, 18111): 2157.7624203863165, (42, 18148): 1867.6504537795543, (42, 18166): 1979.381984937293, (42, 18189): 2084.710432116639, (42, 18239): 97.11418257656223, (42, 18240): 97.92872001096315, (42, 18245): 97.9657810264285, (42, 18247): 97.9521481518919, (42, 18251): 99.00773218668503, (42, 18256): 101.17565664082755, (42, 18258): 100.62051704129613, (42, 18259): 101.29496426378807, (42, 18260): 102.38457152169295, (42, 18262): 103.79255313290103, (42, 18263): 101.96015108889819, (42, 18264): 102.98104921827921, (42, 18266): 104.9121195355144, (42, 18267): 105.79109787915897, (42, 18268): 106.56478014122882, (42, 18269): 108.41722859503739, (42, 18275): 107.5471363441024, (42, 18285): 102.28435839733338, (42, 18308): 83.24926239496156, (42, 18313): 79.17331060300842, (42, 18314): 83.64345952410136, (42, 18315): 105.81300954648299, (42, 18316): 106.8970756320503, (42, 18317): 107.83800318463693, (42, 18320): 106.97117863262395, (42, 18321): 108.03009898324765, (42, 18322): 109.26403767526216, (42, 18324): 108.55455135548935, (42, 18325): 110.73150320739879, (42, 18326): 109.86489989496157, (42, 18327): 109.7274426577036, (42, 18329): 110.41269390699847, (42, 18330): 113.00261463530425, (42, 18331): 110.9643440715287, (42, 18332): 109.49263197813764, (42, 18333): 111.70677669431281, (42, 18336): 108.70850789693795, (42, 18337): 108.7018548956174, (42, 18403): 114.42819181976205, (42, 18432): 132.526660794824, (42, 18451): 118.34643011598607, (42, 18466): 110.64895670240543, (42, 18481): 103.26690142349781, (42, 18483): 104.08491329556202, (42, 18484): 102.24634706682728, (42, 18485): 95.886949687265, (42, 18486): 96.38742791452414, (42, 18487): 92.57611451445216, (42, 18489): 98.680924789263, (42, 18490): 99.43821406479613, (42, 18491): 100.79890704919423, (42, 18492): 90.32790641189973, (42, 18493): 95.0016233615054, (42, 18494): 98.78627116580296, (42, 18495): 98.31172079267981, (42, 18496): 97.52161582851933, (42, 18497): 91.00031200592068, (42, 18498): 94.79796202834727, (42, 18499): 97.18891710746077, (42, 18501): 94.07912004505657, (42, 18502): 92.45562174775777, (42, 18503): 92.16172798585936, (42, 18504): 99.04207672545456, (42, 18506): 92.13682771551268, (42, 18507): 90.1650268067821, (42, 18508): 96.09713905510091, (42, 18509): 95.39523034442607, (42, 18510): 91.10971486147727, (42, 18511): 93.9561615497082, (42, 18512): 93.54820724789128, (42, 18515): 98.08077215004131, (42, 18516): 95.72121169558139, (42, 18517): 92.62019805035366, (42, 18518): 97.63680981437089, (42, 18519): 99.82495299922051, (42, 18520): 96.58366058209741, (42, 18522): 107.75412333798242, (42, 18523): 107.20181985669419, (42, 18532): 108.01622206475828, (42, 18535): 105.47211908399291, (42, 18537): 104.09875504797702, (42, 18539): 103.92297334466913, (42, 18540): 103.60079457614908, (42, 18541): 103.89595975451131, (42, 18542): 104.17361865543621, (42, 18543): 102.48934312295397, (42, 18546): 101.81923221999708, (42, 18555): 104.01771133875796, (42, 18556): 103.87621604489118, (42, 18565): 106.72858992816626, (42, 18567): 105.80203579114867, (42, 18568): 105.24166588896969, (42, 18577): 114.83575044876281, (42, 18583): 115.21279285470445, (42, 18605): 119.76680472362824, (42, 18608): 103.57300622893678, (42, 18616): 128.84084472162027, (42, 18618): 136.01811250545185, (42, 18625): 137.95586598190394, (42, 18645): 133.41320380963816, (42, 18646): 133.27954434514183, (42, 18653): 121.63273267892484, (42, 18654): 127.81748347916421, (42, 18655): 122.64478712326925, (42, 18666): 157.61610627083397, (42, 18837): 246.76658541624005, (42, 18974): 144.96849774305983, (42, 18999): 162.33106300998148, (42, 19000): 163.6678706419168, (42, 19174): 254.99091704279252, (42, 19342): 265.44850487737847, (42, 19455): 185.5346541574891, (42, 19555): 316.8268534491263, (42, 19564): 337.14299109570817, (42, 19573): 335.802483294468, (42, 19586): 333.5606030688741, (42, 19605): 327.4845233264198, (42, 19611): 327.14002378816247, (42, 19614): 319.9881959888483, (42, 19641): 288.770297101612, (42, 19702): 299.2076195705225, (42, 19713): 298.66770411198604, (42, 19731): 303.58320436712603, (42, 19819): 217.42515520092758, (42, 19893): 447.862663844729, (42, 19899): 460.5470332689209, (42, 19929): 443.3742843787578, (42, 19951): 447.0946641298313, (42, 19962): 457.06240479794536, (42, 19970): 428.0704948589482, (42, 19971): 434.71989858762703, (42, 19972): 439.69173951808585, (42, 19975): 435.1575454439649, (42, 19978): 417.2184823382698, (42, 19987): 412.59303332708845, (42, 19989): 410.2952910166703, (42, 20039): 410.80263601445955, (42, 20043): 405.47164707769184, (42, 20047): 398.5463541262008, (42, 20052): 401.38599118969034, (42, 20054): 404.6165802378419, (42, 20085): 381.44620578074364, (42, 20104): 382.1789594781153, (42, 20132): 386.4080204154903, (42, 20203): 508.3110881571922, (42, 20280): 528.4358136313572, (42, 20285): 536.8197159806994, (42, 20290): 524.3760423793813, (42, 20297): 523.3560143439419, (42, 20309): 468.9910603067343, (42, 20453): 447.4604747188398, (42, 20485): 522.0490335938389, (42, 20520): 521.5262727754647, (42, 20526): 541.6220646188434, (42, 20698): 1391.2346377238964, (42, 20868): 1605.5748319167208, (42, 21042): 495.20632893773893, (42, 21057): 451.2655478161624, (42, 21066): 473.46854478450376, (42, 21075): 480.81025981160553, (42, 21093): 492.9676513659075, (42, 21098): 463.8141064498169, (42, 21127): 492.10770117680744, (42, 21130): 484.36329757024555, (42, 21144): 484.6078098024105, (42, 21146): 494.98038429470233, (42, 21147): 485.10950774538446, (42, 21148): 477.75768050589016, (42, 21153): 495.1460198987257, (42, 21293): 423.6470814257782, (42, 21426): 442.3249812766353, (42, 21442): 405.58529926028586, (42, 21451): 402.1015187659548, (42, 21466): 421.9170135471223, (42, 21469): 414.9291663442462, (42, 21471): 425.52451428148277, (42, 21473): 419.3922551535979, (42, 21475): 424.4855123102235, (42, 21482): 411.74074853636944, (42, 21484): 412.541972254972, (42, 21488): 416.9726903317523, (42, 21494): 422.95442889997133, (42, 21498): 418.1350282032034, (42, 21500): 424.614786911765, (42, 21514): 406.5425463183071, (42, 21537): 423.17844428917783, (42, 21662): 398.1535988712063, (42, 21691): 424.8551047254525, (42, 21757): 479.7924242736357, (42, 21777): 585.2294570512514, (42, 21778): 591.9410932280578, (42, 21779): 589.2879292490378, (42, 21790): 576.5535704181152, (42, 21802): 578.9996942981577, (42, 21824): 573.2207729778161, (42, 21874): 588.9995021063935, (42, 21879): 595.2976900526844, (42, 21983): 556.8565969632288, (42, 22002): 490.830339605574, (42, 22132): 530.2223396402027, (42, 22261): 1492.4307670429544, (42, 22298): 1479.9074625796102, (42, 22339): 1564.0459874751534, (42, 22508): 1357.6289984865466, (42, 22841): 2844.9007057605363, (42, 22842): 2845.306262132149, (42, 22874): 2830.102294793301, (42, 22941): 2830.5282421925795, (42, 22956): 2840.911347223444, (42, 22960): 2842.986246636254, (42, 22968): 2857.8836771847937, (42, 22970): 2859.945743995616, (42, 22974): 2867.9221434613837, (42, 22980): 2880.047052254106, (42, 23025): 2882.965869671338, (42, 23028): 2881.0874491348413, (42, 23081): 2906.2830262056827, (42, 23104): 2890.5717171865763, (42, 23147): 2772.86810143418, (42, 23298): 285.6520803473813, (42, 23376): 304.71205293507694, (42, 23381): 315.4216108057, (42, 23529): 271.8794556394028, (42, 23556): 283.1642308829539, (42, 23718): 300.71887819641097, (42, 24001): 177.69703075024458, (42, 24094): 133.23684435759787, (42, 24129): 114.22546800397114, (42, 24174): 154.5968698117493, (42, 24235): 113.44961219253027, (42, 24259): 92.77423830647462, (42, 24260): 94.35861246801015, (42, 24261): 98.34696066645584, (42, 24305): 70.51099053191363, (42, 24306): 66.7642353365224, (42, 24307): 72.38057418050691, (42, 24308): 155.57335351342604, (42, 24498): 55.20450239842872, (42, 24499): 54.1630565897656, (42, 24500): 56.21331859069919, (42, 24668): 111.88859969221858, (42, 24711): 30.645199418400807, (42, 24756): 20.413297383798852, (42, 24788): 30.217866752885957, (42, 24809): 0.2005883365037499, (42, 24813): 10.750233426713732, (42, 24821): 7.866159879129327, (42, 24825): 7.7791936057218525, (42, 24832): 1.9254354473003976, (42, 24833): 3.2786995883077488, (42, 24835): 6.026873346861479, (42, 24837): 12.833494928622883, (42, 24840): 1.9045729967094667, (42, 24841): 5.467679520317518, (42, 24844): 2.347437226594139, (42, 24845): 5.952641713102941, (42, 24846): 3.1443278708932363, (42, 24849): 4.112822783237383, (42, 24850): 10.375557397748715, (42, 24863): 38.216596058135806, (42, 24866): 32.40154690253386, (42, 24885): 25.26542693598556, (42, 24886): 24.927019970731536, (42, 24889): 18.717952936834596, (42, 24903): 22.980492769733843, (42, 24909): 35.56923020713497, (42, 24999): 281.3495512244573, (42, 25019): 281.72104389987453, (42, 25028): 276.01796435254585, (42, 25137): 609.8624346808626, (42, 25145): 605.9549499462231, (42, 25208): 647.7434958101499, (42, 25233): 653.79050772447, (42, 25371): 559.7043438535428, (42, 25377): 556.5057048821203, (42, 25828): 800.1816161227388, (42, 25851): 827.667007838234, (42, 25874): 788.3087046804994, (42, 25898): 789.1402039423763, (42, 25946): 803.6196331251147, (42, 26047): 757.5928394312723, (42, 26066): 545.8304756641767, (42, 26197): 663.8023325910073, (42, 26212): 1017.6206676527206, (42, 26253): 1039.4111477367162, (42, 26254): 1029.7687838035977, (42, 26257): 1026.4544668953263, (42, 26258): 1036.2784431778116, (42, 26260): 1030.902651158748, (42, 26266): 1029.5168474835957, (42, 26267): 1024.6141308144172, (42, 26271): 1025.5841338735515, (42, 26304): 944.66273929677, (42, 26305): 942.2641281988083, (42, 26363): 840.3875261149428, (42, 26441): 1526.5344170680828, (42, 26442): 1524.529484656905, (42, 26450): 1513.568334492568, (42, 26459): 1511.737862851509, (42, 26462): 1512.8413391294669, (42, 26467): 1544.8377434082424, (42, 26471): 1536.3560348733877, (42, 26472): 1535.5488858356762, (42, 26473): 1535.3189645712796, (42, 26476): 1531.6355917946803, (42, 26485): 1517.6526720800396, (42, 26493): 1518.487887275986, (42, 26524): 1517.210729713784, (42, 26525): 1516.2193941873857, (42, 26556): 1531.9826459598896, (42, 26560): 1530.1195656984044, (42, 26561): 1523.0159472560663, (42, 26564): 1529.2513053307425, (42, 26569): 1521.5983671317306, (42, 26570): 1519.1548482709345, (42, 26573): 1521.3584537897607, (42, 26581): 1521.5120874089691, (42, 26583): 1518.8710272324859, (42, 26593): 1522.1051639876516, (42, 26837): 1547.4170945153085, (42, 26844): 1554.536298007739, (42, 26863): 1540.0357242091393, (42, 26893): 1560.9261010680302, (42, 26902): 1570.6272146537, (42, 26905): 1559.9182433619715, (42, 26912): 1567.7739614057812, (42, 26921): 1549.9804843417191, (42, 26922): 1531.9923269531657, (42, 27212): 1576.4198331556313, (42, 27218): 1566.742966862065, (42, 27239): 1590.6202051457874, (42, 27257): 1583.633842219643, (42, 27274): 1593.6371480299913, (42, 27279): 1592.4071620153939, (42, 27282): 1584.1372570719475, (42, 27283): 1586.760305007545, (42, 27285): 1597.5795783673163, (42, 27286): 1590.576655652528, (42, 27290): 1577.1228470450753, (42, 27295): 1571.5324531650442, (42, 27300): 1594.9335051154842, (42, 27344): 1574.289979396822, (42, 27366): 1583.9727641974139, (42, 27383): 1598.9909230922517, (42, 27398): 1608.2784328654784, (42, 27406): 1599.8129647914438, (42, 27407): 1601.9925079708237, (42, 27426): 1588.9111318352027, (42, 27432): 1553.8058668368208, (42, 27460): 1575.4870829467886, (42, 27523): 1591.9264308375823, (42, 27545): 1732.7377052838904, (42, 27602): 1923.3035096941446, (42, 27606): 1926.371067732555, (42, 27646): 1735.430788841861, (42, 27667): 1773.2965268326966, (42, 27672): 1775.03706929338, (42, 27674): 1768.7344226037983, (42, 27688): 1773.1736199191862, (42, 27692): 1781.8669138401442, (42, 27693): 1776.2496429073715, (42, 27705): 1776.2304616986244, (42, 27712): 1779.2270938892798, (42, 27786): 1920.9674488727665, (42, 27790): 1895.4939215011168, (42, 27791): 1893.0908102499102, (42, 27795): 1910.6599304452557, (42, 27801): 1892.072634456043, (42, 27813): 1927.2779967573529, (42, 27816): 1919.5518512301226, (42, 27823): 1891.3300740242967, (42, 27830): 1910.2298010840989, (42, 27884): 1675.2120005226477, (42, 27885): 1719.976075961949, (42, 27896): 1692.759048312647, (42, 27919): 1690.6161286991617, (42, 27922): 1696.5963167493903, (42, 27930): 1681.6588249311033, (42, 27934): 1683.6199058705013, (42, 27935): 1685.167779912275, (42, 27948): 1916.2690925491027, (42, 27951): 1922.8387356116464, (42, 28061): 1760.3235219251121, (42, 28290): 2150.5696270810336, (42, 28292): 2158.6538350487567, (42, 28293): 2152.14919141588, (42, 28295): 2148.79047520764, (42, 28296): 2150.176651985863, (42, 28297): 2146.270697926314, (42, 28302): 2143.4508360475847, (42, 28310): 2260.361221176987, (42, 28313): 2265.1772054940516, (42, 28372): 2268.823531422153, (42, 28398): 2269.275072132761, (42, 28399): 2266.5086541822247, (42, 28400): 2270.6684597198964, (42, 28401): 2260.064890224354, (42, 28445): 2260.515856216104, (42, 28475): 2253.4223466425474, (42, 28885): 156.78705716399452, (42, 28886): 162.12424606460695, (42, 28915): 170.13430145071732, (42, 28916): 169.0420519221466, (42, 28917): 172.78747650153107, (42, 28921): 149.3349249634664, (42, 28931): 152.81291691449567, (42, 28945): 202.28506501157852, (42, 28982): 186.83522448768886, (42, 29219): 239.62985629054035, (42, 29228): 244.524831667562, (42, 29246): 270.26040747227614, (42, 29248): 284.4898805898657, (42, 29282): 277.95320040374304, (42, 29290): 257.664987787593, (42, 29291): 260.6784659566242, (42, 29292): 259.91622576859345, (42, 29293): 257.5474248823104, (42, 29294): 265.50531217012264, (42, 29298): 261.51020576936804, (42, 29299): 265.1733019892967, (42, 29304): 254.72249428595285, (42, 29317): 245.96452590264641, (42, 29323): 244.93613124511154, (42, 29330): 249.50789148278128, (42, 29331): 248.74517658026087, (42, 29344): 265.9794058539875, (42, 29445): 399.6985553196881, (42, 29724): 2797.3033189415337, (42, 29738): 2800.57234395463, (42, 29745): 2790.2495137779006, (42, 29748): 2788.1251081548708, (42, 29750): 2791.769612955779, (42, 29759): 2784.1369474606886, (42, 29772): 2796.154302810768, (42, 29781): 2793.41507083525, (42, 29784): 2793.0791958973277, (42, 29790): 2795.323041848759, (42, 29811): 2786.692026453643, (42, 29817): 2798.2556488201662, (42, 29818): 2795.514866702909, (42, 29929): 2791.586142736497, (42, 30039): 2844.961053328749, (42, 30066): 2823.5154252148313, (42, 30116): 2704.244309788054, (42, 30238): 2527.83931915628, (42, 30248): 2625.6572538954347, (42, 30260): 2628.568664780199, (42, 30545): 178.0468001462459, (42, 30733): 342.50979167816286, (42, 30756): 401.6730351336042, (42, 30921): 312.828291476764, (42, 31079): 819.2848710015701, (42, 31149): 814.5811882446445, (42, 31154): 817.9576278818319, (42, 31160): 815.2478858716349, (42, 31163): 820.2703622910325, (42, 31189): 875.371222181397, (42, 31215): 874.995422746498, (42, 31259): 898.2695922426144, (42, 31262): 903.2145678952606, (42, 31430): 827.5854174268807, (42, 31568): 1018.9239086184195, (42, 31751): 859.6187278899624, (43, 109): 1718.890691006376, (43, 872): 4.992693790498232, (43, 873): 3.7347726555673812, (43, 877): 5.143085260231416, (43, 879): 6.0647455029611805, (43, 884): 14.420062777973845, (43, 889): 12.399502600583794, (43, 891): 14.385204169307665, (43, 892): 10.374133753857242, (43, 894): 8.296643824737531, (43, 896): 4.4765188387953785, (43, 903): 9.97796257520143, (43, 909): 15.570234659191975, (43, 910): 14.770423910890566, (43, 912): 19.318601460919137, (43, 913): 24.087962953473667, (43, 916): 28.968759617843205, (43, 926): 16.727808793457047, (43, 927): 19.5341408940276, (43, 948): 15.523144490324434, (43, 961): 9.863650997237336, (43, 962): 10.886420593226475, (43, 963): 11.819258265995304, (43, 967): 10.11456034727567, (43, 974): 17.682063067646126, (43, 998): 15.46632257531551, (43, 1014): 186.31782239721997, (43, 1086): 121.1523425497709, (43, 1087): 135.17068113320292, (43, 1089): 131.72804356995331, (43, 1090): 128.9126035603787, (43, 1092): 123.58643321513135, (43, 1097): 124.90268594232857, (43, 1107): 130.01389074574064, (43, 1387): 1330.0751030699903, (43, 1554): 1442.6543833676744, (43, 1827): 420.5915060612597, (43, 1828): 420.5587668118824, (43, 1829): 422.4810050126968, (43, 1830): 425.580615748882, (43, 1831): 425.5335338594421, (43, 1832): 424.19656431193994, (43, 1833): 423.5335759108924, (43, 1836): 421.7080089444458, (43, 1841): 428.21695733345564, (43, 1843): 425.9580620780685, (43, 1844): 427.72143778068255, (43, 1845): 425.70493111680565, (43, 1847): 414.75610000863395, (43, 1848): 418.02781344000516, (43, 1849): 434.1195168346479, (43, 1850): 435.0200143656556, (43, 1851): 422.5768116724481, (43, 1852): 424.60821132169684, (43, 1854): 424.7508760631307, (43, 1856): 416.6448290778243, (43, 1857): 418.7700262913716, (43, 1858): 431.4090056521314, (43, 1861): 423.7701856441834, (43, 1866): 417.9964557844308, (43, 1867): 426.899714738731, (43, 1868): 423.6698433214645, (43, 1870): 429.76823155362734, (43, 1871): 425.03537037022267, (43, 1875): 423.3824356360146, (43, 1880): 417.0690711472636, (43, 1882): 420.5704824009316, (43, 1883): 433.1566555252874, (43, 1889): 415.8019222202098, (43, 1893): 419.8631360282154, (43, 1894): 417.2069334889588, (43, 1899): 412.7041631049927, (43, 1900): 413.72053451630154, (43, 1902): 423.6384005219729, (43, 1905): 427.55002912131874, (43, 1907): 418.35925699811554, (43, 1910): 417.26453626026546, (43, 1917): 428.05777570449254, (43, 1920): 417.04731605677176, (43, 1935): 424.7154877918869, (43, 1937): 427.6511528065541, (43, 1946): 404.0464149309347, (43, 1949): 405.81766027231015, (43, 1950): 400.9107793460136, (43, 1951): 404.18719095497215, (43, 1952): 411.97205787392835, (43, 1953): 409.2591405472274, (43, 1954): 410.20649853499924, (43, 1958): 406.8774841342532, (43, 1960): 412.38654065292724, (43, 1968): 414.5514724012543, (43, 1969): 422.0986345740747, (43, 1974): 420.37775781187423, (43, 1975): 421.41336371819534, (43, 1979): 413.15728043360366, (43, 1980): 415.8970203024041, (43, 1981): 415.6536170904686, (43, 1985): 416.2455057585752, (43, 1994): 405.44057143448055, (43, 2011): 421.6687008854621, (43, 2019): 448.0689777294555, (43, 2020): 444.60384390044834, (43, 2029): 434.967176764631, (43, 2030): 442.14600081250785, (43, 2032): 435.24999433132507, (43, 2033): 438.5454650277602, (43, 2034): 440.24905309474434, (43, 2036): 437.80747389837074, (43, 2037): 438.0778419836838, (43, 2038): 430.35505144494965, (43, 2042): 464.6428711979565, (43, 2050): 434.4223200818445, (43, 2051): 435.83816683291275, (43, 2053): 435.90589784920104, (43, 2054): 439.0033835446947, (43, 2066): 433.0377813539527, (43, 2067): 432.07854473582483, (43, 2071): 398.8061251657471, (43, 2072): 402.97323349503773, (43, 2073): 382.93494193089964, (43, 2074): 383.35155356514787, (43, 2080): 377.0044624744213, (43, 2082): 405.65060535655306, (43, 2083): 407.7103699658846, (43, 2089): 400.37352520581186, (43, 2090): 401.996963062818, (43, 2092): 397.3757830987563, (43, 2098): 378.1395877292659, (43, 2099): 382.4298634353066, (43, 2101): 379.2116656198644, (43, 2102): 391.95359256997403, (43, 2103): 388.59570839455955, (43, 2104): 387.5530968129314, (43, 2106): 410.337175519133, (43, 2112): 382.44977673851724, (43, 2113): 394.77098020690744, (43, 2114): 400.6722125284189, (43, 2117): 413.71234308508434, (43, 2123): 344.35410930267597, (43, 2124): 347.2998658578312, (43, 2134): 341.0505332471559, (43, 2138): 348.80174023703813, (43, 2141): 341.3853287411686, (43, 2148): 355.4807979943123, (43, 2150): 334.67448818911726, (43, 2151): 338.39651281804703, (43, 2152): 333.6659888630308, (43, 2153): 355.38805706574203, (43, 2154): 342.84253511540084, (43, 2155): 343.4111582876595, (43, 2156): 339.8226370892347, (43, 2157): 350.32319415972904, (43, 2160): 357.14391491242077, (43, 2161): 334.07464496610993, (43, 2162): 360.23348876010226, (43, 2163): 355.8523745172916, (43, 2164): 356.3221674854246, (43, 2168): 340.73989405175087, (43, 2172): 348.4240821474883, (43, 2174): 339.19005513533375, (43, 2178): 352.32860578236705, (43, 2179): 350.947014597615, (43, 2183): 349.5676971929546, (43, 2185): 350.28499295846774, (43, 2186): 347.6652737687043, (43, 2190): 356.6936707178097, (43, 2192): 352.16098770602036, (43, 2193): 350.09644176044577, (43, 2194): 345.47246429971034, (43, 2195): 345.94368020943523, (43, 2197): 353.7541665448486, (43, 2205): 349.0870666579851, (43, 2207): 342.73359494201077, (43, 2208): 346.5413153503437, (43, 2212): 349.13014129422754, (43, 2214): 283.34627832467856, (43, 2225): 299.57680572359044, (43, 2231): 245.07758220218483, (43, 2278): 356.3481924133517, (43, 2284): 368.85257096338313, (43, 2285): 369.1555010386895, (43, 2291): 362.70297005376466, (43, 2292): 351.57317425838795, (43, 2307): 363.4504660840792, (43, 2313): 364.9779507204441, (43, 2317): 340.12305226320234, (43, 2319): 355.81343844056624, (43, 2321): 361.9037223042436, (43, 2323): 357.86795237150665, (43, 2326): 367.1527997178442, (43, 2327): 363.2746741869297, (43, 2329): 360.96622481331974, (43, 2330): 359.12105052316485, (43, 2332): 367.0363232291416, (43, 2344): 352.45734123946, (43, 2346): 354.5595775532522, (43, 2361): 335.38780611701804, (43, 2368): 390.9317740048521, (43, 2374): 396.84502604177834, (43, 2375): 397.28521132971935, (43, 2377): 380.5709657066081, (43, 2378): 400.90072059624816, (43, 2379): 403.34878012682873, (43, 2380): 403.38995718842375, (43, 2383): 383.4231467534047, (43, 2385): 385.09566364297837, (43, 2395): 383.62579432060267, (43, 2397): 402.48006316023293, (43, 2398): 375.47246774008016, (43, 2399): 380.0725931572607, (43, 2400): 378.78846544112696, (43, 2402): 393.3220978719171, (43, 2403): 396.90272522605295, (43, 2404): 396.96703420379293, (43, 2405): 389.11007639200034, (43, 2407): 394.2751808498522, (43, 2408): 399.3605870864128, (43, 2409): 391.16309463034526, (43, 2411): 400.4332746607896, (43, 2412): 398.14791091182906, (43, 2413): 401.57181938753126, (43, 2414): 397.29489144297395, (43, 2422): 400.6145968667604, (43, 2424): 398.37623894913514, (43, 2426): 398.43203439010455, (43, 2433): 393.18668753169374, (43, 2436): 393.7984964107062, (43, 2437): 372.4509699665833, (43, 2440): 376.496651835704, (43, 2445): 488.11828218847063, (43, 2447): 474.73604329271717, (43, 2454): 485.1598099208111, (43, 2455): 483.8815101559754, (43, 2460): 454.05509036807695, (43, 2461): 458.13907962334093, (43, 2471): 532.9742367513246, (43, 2492): 557.525162110354, (43, 2511): 511.7935967580355, (43, 2523): 535.5442242120902, (43, 2525): 536.8358439796301, (43, 2535): 492.41447013245175, (43, 2537): 487.3626232238857, (43, 2538): 488.4893212174225, (43, 2539): 498.3756863612458, (43, 2540): 495.01648682068, (43, 2542): 502.7520318617269, (43, 2559): 573.0493996758426, (43, 2575): 576.4891895007678, (43, 2599): 406.8561978350794, (43, 2600): 445.100424779268, (43, 2607): 414.84431313545207, (43, 2627): 575.6875609209274, (43, 2647): 600.7730290557002, (43, 2674): 578.0357135690072, (43, 2681): 582.8608021646421, (43, 2683): 587.4819213911184, (43, 2686): 575.1033232097354, (43, 2689): 688.6292838322713, (43, 2690): 690.7361602950837, (43, 2713): 759.984897274377, (43, 2714): 768.5168241295502, (43, 2715): 770.8143890969283, (43, 2739): 766.7899240699924, (43, 2740): 733.5332283945079, (43, 2741): 733.3705990654303, (43, 2749): 770.7399348760811, (43, 2750): 769.0509959847097, (43, 2752): 769.5996716680108, (43, 2755): 772.9400768661985, (43, 2758): 774.4274499451178, (43, 2759): 773.3549290065979, (43, 2769): 767.9331096902515, (43, 2771): 742.147378152924, (43, 2779): 760.3375005237452, (43, 2784): 742.178826801011, (43, 2800): 764.6917890830191, (43, 2802): 738.2769489933056, (43, 2803): 735.1937371970523, (43, 2804): 732.7550504020727, (43, 2805): 746.8878169859992, (43, 2807): 744.5128131494, (43, 2809): 748.6228596538566, (43, 2812): 727.966070041541, (43, 2814): 762.7507197319201, (43, 2817): 783.7055251451551, (43, 2819): 739.387336430757, (43, 2823): 749.0377269116549, (43, 2832): 752.9657509200824, (43, 2836): 742.0925023844562, (43, 2839): 742.2236098415119, (43, 2841): 773.8187243899227, (43, 2843): 769.3795181636422, (43, 2846): 753.3276961743835, (43, 2849): 758.433259755377, (43, 2852): 754.5299067977712, (43, 2853): 760.3678542340075, (43, 2876): 771.9182509787188, (43, 2877): 782.1635479617507, (43, 2885): 806.214165448066, (43, 2918): 726.6013527621117, (43, 2921): 733.0608535767484, (43, 2925): 695.7609557471751, (43, 2926): 679.3567115441729, (43, 2930): 727.7376690491172, (43, 2931): 703.4025365005044, (43, 2938): 730.442272614598, (43, 2940): 724.1738161915109, (43, 2947): 706.0333934330185, (43, 2949): 718.98224391131, (43, 2950): 724.4671455774535, (43, 2952): 722.6630532682673, (43, 2958): 720.7444460311937, (43, 2959): 718.2670702299524, (43, 2960): 724.000117382948, (43, 2961): 723.6479055242493, (43, 2963): 721.3012325768282, (43, 2968): 724.7559770865498, (43, 2976): 718.509684350072, (43, 2981): 711.328077100242, (43, 2982): 715.1143310567691, (43, 2984): 714.4892712957105, (43, 3003): 716.7786086781829, (43, 3046): 640.0633497438785, (43, 3050): 683.4034813678375, (43, 3051): 682.991057602853, (43, 3053): 681.131964011136, (43, 3069): 710.4300784215583, (43, 3071): 669.4710708122662, (43, 3080): 814.0658939100844, (43, 3199): 741.0017229196009, (43, 3200): 740.6427172761524, (43, 3205): 760.8304164149317, (43, 3209): 743.1179689462367, (43, 3215): 738.1452075902779, (43, 3217): 734.3924657540803, (43, 3249): 735.6293603612938, (43, 3263): 764.0173591534234, (43, 3289): 737.1749476633615, (43, 3301): 745.0761598277209, (43, 3302): 741.108078240648, (43, 3307): 738.6282907435631, (43, 3310): 746.7572004372316, (43, 3391): 887.9388467783667, (43, 3509): 695.3600375430188, (43, 3510): 698.9604581255795, (43, 3511): 694.4244842584177, (43, 3512): 694.8147753531662, (43, 3514): 692.3861928041924, (43, 3519): 697.857014739338, (43, 3536): 685.2270113160347, (43, 3545): 677.398018695922, (43, 3548): 680.1629644489844, (43, 3572): 685.8162174439714, (43, 3581): 697.4437824778636, (43, 3583): 690.932093984424, (43, 3601): 694.9159044047063, (43, 3656): 709.3867138868519, (43, 3669): 735.6672554005457, (43, 3670): 733.598781272959, (43, 3695): 742.3433214003919, (43, 3696): 739.6124761944119, (43, 3782): 644.978125650424, (43, 3792): 654.0399454745883, (43, 3989): 2590.8697903801844, (43, 4008): 2615.838141187555, (43, 4031): 2614.0155055538985, (43, 4045): 2605.349156940752, (43, 4144): 2606.837731444128, (43, 4145): 2581.812806198348, (43, 4164): 2597.210161238677, (43, 4168): 2589.445639897648, (43, 4173): 2587.8628972332735, (43, 4181): 2572.6148926165065, (43, 4228): 2558.142084850151, (43, 4248): 2551.936693525891, (43, 4254): 2413.1427575624316, (43, 4260): 2413.9301523451877, (43, 4262): 2422.6513909467553, (43, 4273): 2420.889037766057, (43, 4319): 2334.2853571166584, (43, 4326): 2331.584711808702, (43, 4328): 2332.8371217676618, (43, 4334): 2337.749473539023, (43, 4335): 2335.6068659525017, (43, 4372): 2107.9114330145608, (43, 4413): 2171.012608178712, (43, 4434): 2106.877791882262, (43, 4447): 2121.7139396842213, (43, 4452): 2106.946973897449, (43, 4463): 1927.0556902968863, (43, 4465): 1934.2462950379145, (43, 4619): 2160.782724460035, (43, 4645): 2180.9177237957256, (43, 4657): 2175.837010306404, (43, 4666): 2167.0204439845293, (43, 4676): 2179.137138813264, (43, 4678): 2182.9610759007123, (43, 4689): 2171.890891876035, (43, 4704): 2231.668609463439, (43, 4726): 2324.588855548351, (43, 4727): 2322.6286073972215, (43, 4730): 2319.006646946389, (43, 4731): 2318.873307848688, (43, 4734): 2327.7176840315933, (43, 4735): 2324.8523276822307, (43, 4736): 2324.912551595754, (43, 4737): 2320.426408790767, (43, 4738): 2320.1577218803727, (43, 4756): 2321.5788995828793, (43, 4760): 2316.7018154798047, (43, 4761): 2319.798799454453, (43, 4762): 2312.819252186231, (43, 4765): 2317.0702984797413, (43, 4773): 2329.4320285615845, (43, 4774): 2325.987367157043, (43, 4790): 2328.3815351607436, (43, 4795): 2327.091723697914, (43, 4799): 2325.9395612166823, (43, 4801): 2327.738935115298, (43, 4804): 2329.877903979586, (43, 4805): 2328.7936902383703, (43, 4806): 2322.745556484525, (43, 4815): 2319.374482303066, (43, 4816): 2325.064788334184, (43, 4817): 2324.090569363995, (43, 4826): 2321.757719786286, (43, 4830): 2318.135226490465, (43, 4839): 2322.307501521515, (43, 4840): 2323.2203967998903, (43, 4841): 2318.413451582334, (43, 4846): 2317.3855142628927, (43, 4848): 2315.25814781111, (43, 4850): 2316.751251628715, (43, 4871): 2301.786116119675, (43, 4883): 2316.947846560873, (43, 4900): 2311.50947399492, (43, 4901): 2307.7365646245235, (43, 4917): 2126.5853918659855, (43, 4931): 2110.4741717375855, (43, 4944): 2129.6971784057164, (43, 4956): 2112.14284792425, (43, 4958): 2109.1370534064395, (43, 4959): 2104.337978301035, (43, 4961): 2116.4420210404533, (43, 4966): 2106.734287904377, (43, 5207): 2088.6410521496373, (43, 5272): 1875.5169045342618, (43, 5283): 1880.1144379375978, (43, 5287): 1881.1705743701689, (43, 5289): 1882.9659973183263, (43, 5293): 1882.5671637158143, (43, 5295): 1896.343197947477, (43, 5296): 1892.3970120546667, (43, 5298): 1890.0874872867857, (43, 5303): 1890.8896595448152, (43, 5305): 1865.1675331730999, (43, 5306): 1855.865544934322, (43, 5307): 1862.2996783131778, (43, 5308): 1866.1565992614892, (43, 5313): 1870.8323292459986, (43, 5314): 1875.3807271201504, (43, 5317): 1863.6609733699731, (43, 5319): 1885.1911969619373, (43, 5324): 1885.3468143716698, (43, 5326): 1885.6777408149464, (43, 5348): 1851.3886130517456, (43, 5351): 1849.585353733323, (43, 5399): 1880.1526738369669, (43, 5413): 1847.3130001253585, (43, 5422): 1886.6557633657942, (43, 5445): 1873.5699538397594, (43, 5448): 1868.7767019641096, (43, 5456): 1863.5595856996983, (43, 5467): 1866.931871219279, (43, 5624): 1827.987199011922, (43, 5671): 2035.2355742314903, (43, 5672): 2029.0474369381132, (43, 5797): 2112.956137666857, (43, 5871): 1913.4861523681896, (43, 5976): 1853.3363278650538, (43, 6118): 749.8406967211587, (43, 6248): 872.0646067989505, (43, 6345): 1696.5845832007365, (43, 6352): 1679.1606967452162, (43, 6354): 1699.9771787497614, (43, 6359): 1705.0020475661747, (43, 6376): 1685.8762767839726, (43, 6378): 1698.0816437382687, (43, 6381): 1704.6678134733704, (43, 6383): 1692.2461426480086, (43, 6396): 1709.0402835772845, (43, 6399): 1698.7192376708142, (43, 6408): 1678.178439757312, (43, 6409): 1682.2223097090546, (43, 6419): 1647.3950534723858, (43, 6422): 1677.1595999312362, (43, 6423): 1675.5143973448482, (43, 6424): 1693.6456625747483, (43, 6439): 1688.9566510952118, (43, 6464): 1682.805912550463, (43, 6465): 1682.442151522023, (43, 6469): 1687.6157223849782, (43, 6470): 1687.234180486076, (43, 6472): 1711.548536447634, (43, 6480): 1701.1437517586346, (43, 6486): 1704.8678503049182, (43, 6497): 1703.2400560400063, (43, 6503): 1676.0863793578108, (43, 6508): 1681.5570270796954, (43, 6509): 1683.0809894380625, (43, 6521): 1700.4131659948184, (43, 6544): 1695.177926035855, (43, 6552): 1672.9708168386123, (43, 6553): 1669.7814291784057, (43, 6554): 1666.5919174309097, (43, 6578): 1678.9002048570248, (43, 6582): 1672.3756841043364, (43, 6601): 1679.445017892728, (43, 6609): 1708.597964284514, (43, 6610): 1708.5710208155788, (43, 6611): 1711.4988098232443, (43, 6614): 1711.3126800999135, (43, 6615): 1711.0563124631522, (43, 6616): 1711.2135702463677, (43, 6617): 1710.877679957873, (43, 6618): 1712.3448165194466, (43, 6619): 1708.631155543876, (43, 6620): 1709.8500441947833, (43, 6621): 1706.9647651333942, (43, 6622): 1708.5609438981182, (43, 6623): 1709.4477221309426, (43, 6624): 1705.6271324790937, (43, 6625): 1705.9208977215478, (43, 6626): 1709.1247707880061, (43, 6627): 1711.9559830539542, (43, 6628): 1707.8645265051134, (43, 6629): 1704.5807604686781, (43, 6630): 1706.0309673626896, (43, 6632): 1705.1122019656193, (43, 6634): 1702.3012605931056, (43, 6635): 1706.804388413331, (43, 6636): 1710.863366393511, (43, 6637): 1700.8614219004994, (43, 6638): 1704.9574223492907, (43, 6639): 1711.3683259775135, (43, 6640): 1706.1297455815425, (43, 6641): 1705.784450015468, (43, 6642): 1704.0500580262453, (43, 6643): 1709.8758918840945, (43, 6645): 1708.3309397536834, (43, 6646): 1712.5318186459938, (43, 6647): 1705.366788308577, (43, 6653): 1711.3876083535488, (43, 6655): 1711.8733442147027, (43, 6658): 1701.5388400615016, (43, 6662): 1702.8658211419993, (43, 6819): 1535.4365870745528, (43, 6996): 1566.3363517517123, (43, 7059): 1602.6594448800847, (43, 7187): 1505.367812599245, (43, 7304): 1446.820936187625, (43, 7528): 1546.8667463192626, (43, 7720): 1776.6974128309137, (43, 7793): 1766.8452415148117, (43, 7807): 1771.5614854943358, (43, 7808): 1764.554345661929, (43, 7831): 1718.0300522152784, (43, 7850): 1758.5927410294976, (43, 7852): 1752.7630478454646, (43, 8012): 1774.3771849615212, (43, 8125): 1770.4965007065668, (43, 8208): 1843.0588139337756, (43, 8392): 1724.5922443133752, (43, 8651): 1364.7280502737194, (43, 9088): 1553.8327304821305, (43, 9443): 1212.2763751534571, (43, 9444): 1216.7028962904542, (43, 9828): 1028.1725584746957, (43, 9868): 1045.4014114235322, (43, 10180): 1772.077445516876, (43, 10256): 1865.4716653248113, (43, 10276): 1825.9172529547084, (43, 10378): 1850.2094949482394, (43, 10676): 1723.4698753516682, (43, 10714): 1656.5802745439169, (43, 10730): 1680.30068039559, (43, 10862): 1537.4587429032715, (43, 10881): 1552.3347698507464, (43, 10883): 1549.9540507264405, (43, 10885): 1534.4481838593408, (43, 10891): 1546.260333574454, (43, 10909): 1546.6926935299668, (43, 10911): 1550.57309118291, (43, 10913): 1546.5605826493784, (43, 10915): 1547.3334439370478, (43, 10919): 1550.1819390205453, (43, 11037): 1428.6154564752453, (43, 11039): 1398.9300283104956, (43, 11516): 2850.034054472649, (43, 11856): 2340.102308217483, (43, 11857): 2335.032602414247, (43, 11861): 2337.6705878030516, (43, 11881): 2335.417244016787, (43, 11902): 2318.594416389709, (43, 11911): 2316.9738883404193, (43, 11914): 2318.6900387775268, (43, 11922): 2330.695312839089, (43, 11924): 2335.0267298532826, (43, 11926): 2330.2650903898325, (43, 11950): 2341.377166842372, (43, 11963): 2356.98700727248, (43, 11983): 2348.6626393498195, (43, 11985): 2364.6948386717186, (43, 12009): 2363.631293536496, (43, 12010): 2352.055786159917, (43, 12018): 2354.15250140947, (43, 12020): 2356.8774148942675, (43, 12021): 2358.9344643454324, (43, 12024): 2369.5448829200845, (43, 12025): 2365.551459567619, (43, 12027): 2363.139856232644, (43, 12031): 2350.187462141047, (43, 12032): 2353.5633520691927, (43, 12035): 2363.3795248626025, (43, 12041): 2364.837776997086, (43, 12045): 2219.334617399814, (43, 12145): 2289.473652481798, (43, 12275): 2601.712765464369, (43, 12294): 2574.676219934333, (43, 12358): 2664.757384336801, (43, 12463): 2700.726082769947, (43, 12465): 2699.801289439094, (43, 12482): 2713.34141464321, (43, 12503): 2711.6281602031663, (43, 12506): 2715.677388788916, (43, 12549): 2705.1023152791277, (43, 12559): 2702.3792564855503, (43, 12569): 2706.3405900666567, (43, 12572): 2709.3473714156826, (43, 12574): 2702.8639317911307, (43, 12576): 2708.397779456901, (43, 12591): 2706.6076248797594, (43, 12608): 2730.3413526555596, (43, 12696): 2690.340184700252, (43, 12710): 2711.850630980037, (43, 12728): 2702.2128753202524, (43, 12766): 2034.4320437359124, (43, 12771): 1998.6470841398566, (43, 12790): 1994.7146729221884, (43, 12795): 1986.3307311432266, (43, 12797): 1943.3763653177668, (43, 12798): 1948.639083020071, (43, 12811): 1980.722303146254, (43, 12830): 1970.9454449418022, (43, 12848): 1974.569244909868, (43, 12850): 1976.096456559235, (43, 12852): 1968.831288667333, (43, 12854): 1963.9287269880238, (43, 12859): 1978.9348031034724, (43, 12861): 1953.6260476883685, (43, 12865): 1987.605700171452, (43, 12866): 1984.5037211295055, (43, 12867): 1994.8425954647214, (43, 12874): 1989.9087485772654, (43, 12875): 1993.3686936147058, (43, 12881): 1978.8306986527755, (43, 12883): 1984.822874142087, (43, 12885): 1996.7186463022665, (43, 12888): 1981.6302456669744, (43, 12889): 1979.8819611355493, (43, 12892): 1991.1834353287352, (43, 12893): 1982.2533474712798, (43, 12896): 1984.766156794892, (43, 12906): 1992.0286462064819, (43, 13018): 1959.8232036989368, (43, 13071): 1963.0927296969746, (43, 13131): 1913.5128185036242, (43, 13146): 1943.213166358864, (43, 13159): 1913.6839545036778, (43, 13193): 1906.5322896020748, (43, 13198): 1846.0882065396675, (43, 13292): 1909.0688404208322, (43, 13296): 1922.825290389508, (43, 13406): 1819.5060083793624, (43, 13407): 1818.3761696966124, (43, 13417): 1819.7999296952123, (43, 13418): 1826.6994432954023, (43, 13438): 1846.5182671696236, (43, 13442): 1849.5071823800777, (43, 13443): 1845.0778522826279, (43, 13764): 1511.2909858467226, (43, 13766): 1516.6434500190169, (43, 13771): 1515.3343320611527, (43, 13783): 1500.3489099786489, (43, 13784): 1520.8207365179846, (43, 13792): 1511.0650095031133, (43, 13824): 1497.4342046404386, (43, 14017): 1507.9034490542808, (43, 14870): 1575.7509185034762, (43, 14997): 1475.6187632073509, (43, 15000): 1475.6754430372953, (43, 15003): 1479.1845635452562, (43, 15006): 1490.5585503981238, (43, 15007): 1494.5424933811366, (43, 15056): 1492.3745368953046, (43, 15063): 1488.4504140009633, (43, 15069): 1486.5375647811136, (43, 15076): 1494.774316971595, (43, 15086): 1482.8319056285284, (43, 15087): 1477.6315017573822, (43, 15111): 1466.1008174312365, (43, 15116): 1472.6526734924512, (43, 15722): 1366.4960381675853, (43, 15998): 1280.8782128468724, (43, 16073): 1028.2825658338224, (43, 16939): 291.94839555732506, (43, 16940): 287.3181622083512, (43, 16951): 304.0214296982162, (43, 16963): 301.63826645411547, (43, 16965): 302.339496259153, (43, 16969): 308.08581785887264, (43, 16970): 299.6565103139788, (43, 16971): 298.68602422138287, (43, 16973): 302.7652169014235, (43, 16974): 306.5735157949459, (43, 16976): 297.1450072137477, (43, 16978): 294.9556660202119, (43, 16980): 294.0828503574053, (43, 16982): 310.81850471540827, (43, 17045): 704.572760266391, (43, 17048): 709.5600077990458, (43, 17304): 2515.534178201191, (43, 17305): 2511.7800761888975, (43, 17330): 2515.6527960389367, (43, 17334): 2507.2104837855263, (43, 17343): 2521.921703536829, (43, 17345): 2507.406774697965, (43, 17347): 2515.397252483106, (43, 17351): 2496.023544429262, (43, 17372): 2506.483140460875, (43, 17373): 2521.3631892205444, (43, 17377): 2522.447735106733, (43, 17382): 2512.863585206973, (43, 17383): 2514.4801012023718, (43, 17389): 2508.862637801073, (43, 17400): 2518.539255955165, (43, 17401): 2518.269035058319, (43, 17402): 2519.154023378135, (43, 17403): 2520.1497110131254, (43, 17440): 2508.506139398201, (43, 17455): 2520.560345959386, (43, 17491): 2521.817263631166, (43, 17507): 2500.2150907862965, (43, 17509): 2505.3892237620394, (43, 17590): 2493.016160025743, (43, 17615): 2459.9589512842986, (43, 17642): 2465.598651583133, (43, 17643): 2465.3631398814578, (43, 17668): 2459.596571507773, (43, 17721): 2445.67159399031, (43, 17754): 2495.477232765983, (43, 17769): 2501.333142199688, (43, 17776): 2481.17234068711, (43, 17804): 2509.872268267731, (43, 17809): 2515.210091645013, (43, 17824): 2511.362053485043, (43, 17837): 2497.5305733815326, (43, 17838): 2498.4007086539673, (43, 17862): 2494.5691475719227, (43, 17866): 2505.787512005439, (43, 17872): 2490.566790894914, (43, 17873): 2482.061001212911, (43, 17881): 2495.153855572527, (43, 17947): 384.4300928247574, (43, 17951): 395.5219113934857, (43, 17953): 397.86737271421873, (43, 17954): 397.25784559931833, (43, 17959): 386.3191970703327, (43, 17963): 390.05598105697874, (43, 18000): 448.31799023523894, (43, 18001): 445.9282727383115, (43, 18111): 371.59560214476113, (43, 18148): 601.1047304891226, (43, 18166): 513.0168294459961, (43, 18189): 419.52272222502523, (43, 18239): 2523.8905207369207, (43, 18240): 2523.851368719064, (43, 18245): 2524.402622513485, (43, 18247): 2523.2594675833748, (43, 18251): 2524.4120362883505, (43, 18256): 2525.6891215877536, (43, 18258): 2524.3619956119874, (43, 18259): 2524.616071744386, (43, 18260): 2525.1540557896183, (43, 18262): 2526.159745852433, (43, 18263): 2526.0542144423684, (43, 18264): 2526.587910728279, (43, 18266): 2526.577369928994, (43, 18267): 2527.0959993504484, (43, 18268): 2527.359260447819, (43, 18269): 2528.3948642364517, (43, 18275): 2527.906412477705, (43, 18285): 2526.3972404652604, (43, 18308): 2515.470924020599, (43, 18313): 2511.835815603186, (43, 18314): 2513.5775941483134, (43, 18315): 2528.28060573953, (43, 18316): 2528.225292757193, (43, 18317): 2528.71161954211, (43, 18320): 2529.126801632755, (43, 18321): 2529.4075494609606, (43, 18322): 2530.1678509146755, (43, 18324): 2530.745519990714, (43, 18325): 2533.06964977491, (43, 18326): 2532.2023976940604, (43, 18327): 2529.1809998203457, (43, 18329): 2534.0802471025686, (43, 18330): 2533.00953349032, (43, 18331): 2531.440036810666, (43, 18332): 2529.8382544918195, (43, 18333): 2532.741614152592, (43, 18336): 2531.3932322729866, (43, 18337): 2532.163653933666, (43, 18403): 2531.148257744578, (43, 18432): 2500.0749052475053, (43, 18451): 2521.183826050038, (43, 18466): 2541.447036676823, (43, 18481): 2528.8006441321963, (43, 18483): 2528.8241776408718, (43, 18484): 2527.5262078444944, (43, 18485): 2523.589055150059, (43, 18486): 2526.9193802137393, (43, 18487): 2523.9065272284734, (43, 18489): 2526.659126927672, (43, 18490): 2529.552310673231, (43, 18491): 2530.9532650731426, (43, 18492): 2520.9377535277117, (43, 18493): 2526.3853504377025, (43, 18494): 2526.112405809419, (43, 18495): 2528.5039369706656, (43, 18496): 2527.059533554979, (43, 18497): 2523.1837167510785, (43, 18498): 2523.9914055085414, (43, 18499): 2526.1847240716183, (43, 18501): 2524.5441558874045, (43, 18502): 2523.136905390616, (43, 18503): 2522.0945169517586, (43, 18504): 2527.6754319923143, (43, 18506): 2524.663900439335, (43, 18507): 2523.3029431882205, (43, 18508): 2525.8502545086576, (43, 18509): 2525.8494674134813, (43, 18510): 2522.0870698506196, (43, 18511): 2526.7442342649383, (43, 18512): 2525.147065921723, (43, 18515): 2527.7661956863903, (43, 18516): 2527.775044138088, (43, 18517): 2525.951004385415, (43, 18518): 2528.9610022459606, (43, 18519): 2527.995526900082, (43, 18520): 2525.4715345848995, (43, 18522): 2534.004772663714, (43, 18523): 2534.276742731555, (43, 18532): 2536.1735939819537, (43, 18535): 2532.1994271538956, (43, 18537): 2529.9864843206396, (43, 18539): 2530.4320613108116, (43, 18540): 2530.6713043184764, (43, 18541): 2531.745163677267, (43, 18542): 2532.430086614858, (43, 18543): 2529.013413807328, (43, 18546): 2530.5782646739126, (43, 18555): 2534.042896935271, (43, 18556): 2534.6488973867818, (43, 18565): 2535.869781432416, (43, 18567): 2536.8117844230014, (43, 18568): 2534.952975224711, (43, 18577): 2548.5187065459536, (43, 18583): 2546.3440163913483, (43, 18605): 2549.3152931943564, (43, 18608): 2537.8268105653046, (43, 18616): 2561.974686163202, (43, 18618): 2572.6747731141218, (43, 18625): 2569.2702294583646, (43, 18645): 2559.845259620537, (43, 18646): 2562.247197561282, (43, 18653): 2552.9892067434807, (43, 18654): 2561.653655409599, (43, 18655): 2555.901551632442, (43, 18666): 2591.399417846618, (43, 18837): 2555.019355959011, (43, 18974): 2521.6192859997527, (43, 18999): 2531.044710721916, (43, 19000): 2534.332492738043, (43, 19174): 2380.718751851462, (43, 19342): 2448.5626600672063, (43, 19455): 2402.978662314701, (43, 19555): 2243.997927001161, (43, 19564): 2257.207891227611, (43, 19573): 2249.4325144774325, (43, 19586): 2245.734046868938, (43, 19605): 2247.805331501632, (43, 19611): 2252.9278240739272, (43, 19614): 2249.643991259864, (43, 19641): 2330.957543879932, (43, 19702): 2330.606463238176, (43, 19713): 2324.438776186115, (43, 19731): 2211.835696224879, (43, 19819): 2380.133854754771, (43, 19893): 2131.542080217062, (43, 19899): 2160.957892989303, (43, 19929): 2141.0490985954593, (43, 19951): 2206.105517182393, (43, 19962): 2142.948223489399, (43, 19970): 2164.16842476343, (43, 19971): 2162.8686426107274, (43, 19972): 2156.209373098177, (43, 19975): 2154.747568570413, (43, 19978): 2227.268510268476, (43, 19987): 2229.4954461543402, (43, 19989): 2211.4168017735806, (43, 20039): 2233.3586498695527, (43, 20043): 2242.448968557571, (43, 20047): 2238.001638200649, (43, 20052): 2216.748065486047, (43, 20054): 2217.6022667043558, (43, 20085): 2318.926895715003, (43, 20104): 2324.986869590949, (43, 20132): 2286.363214787111, (43, 20203): 2112.95485367931, (43, 20280): 2100.5774520328778, (43, 20285): 2096.611325048302, (43, 20290): 2104.738222330891, (43, 20297): 2098.9113588419523, (43, 20309): 2220.3363214060496, (43, 20453): 2327.2688796815833, (43, 20485): 2061.8141386745438, (43, 20520): 2047.32443179931, (43, 20526): 2036.245870647113, (43, 20698): 1441.954786904373, (43, 20868): 1293.3833654862224, (43, 21042): 1953.8876302196318, (43, 21057): 1998.1784600086532, (43, 21066): 1975.0681290143486, (43, 21075): 1968.7687061617503, (43, 21093): 1955.2660344660385, (43, 21098): 1983.870777362625, (43, 21127): 1956.4901009587043, (43, 21130): 1963.8851623765097, (43, 21144): 1964.4721503653034, (43, 21146): 1953.6082925027306, (43, 21147): 1964.2868528996892, (43, 21148): 1971.3117267389175, (43, 21153): 1960.3170280001384, (43, 21293): 2024.62027991507, (43, 21426): 2031.1302602432515, (43, 21442): 2081.157117161733, (43, 21451): 2085.8954730322944, (43, 21466): 2055.0872154142594, (43, 21469): 2061.639707417842, (43, 21471): 2051.802618215277, (43, 21473): 2057.0059953791038, (43, 21475): 2052.11581535159, (43, 21482): 2066.482967964856, (43, 21484): 2064.747695928412, (43, 21488): 2061.097797394091, (43, 21494): 2051.0932283261873, (43, 21498): 2056.228226435374, (43, 21500): 2047.3260100143941, (43, 21514): 2057.3367846393803, (43, 21537): 2043.6952463429982, (43, 21662): 2060.865601109553, (43, 21691): 2034.2349205584057, (43, 21757): 1994.306766328846, (43, 21777): 1862.4921604470926, (43, 21778): 1855.766424406685, (43, 21779): 1858.5559381881912, (43, 21790): 1871.1119172442868, (43, 21802): 1868.8648468370568, (43, 21824): 1874.902850012457, (43, 21874): 1859.1171230678494, (43, 21879): 1853.3859161770413, (43, 21983): 1891.532732548268, (43, 22002): 1957.564314276679, (43, 22132): 1934.372222812726, (43, 22261): 976.2908378123886, (43, 22298): 992.3771586402753, (43, 22339): 923.1759069659721, (43, 22508): 1107.4618794052533, (43, 22841): 1192.0469706710194, (43, 22842): 1189.171747145963, (43, 22874): 1170.2427223305215, (43, 22941): 1181.0376775978166, (43, 22956): 1184.0147830957849, (43, 22960): 1192.5877121265635, (43, 22968): 1158.5356551000816, (43, 22970): 1165.7654416892112, (43, 22974): 1143.7195997148685, (43, 22980): 1150.3082671865618, (43, 23025): 1114.0415222413174, (43, 23028): 1105.194745634028, (43, 23081): 1072.7885567944886, (43, 23104): 1000.0393742689937, (43, 23147): 1045.1224346999834, (43, 23298): 2169.302660241342, (43, 23376): 2149.628639994197, (43, 23381): 2133.88551694802, (43, 23529): 2178.6327551473887, (43, 23556): 2167.7594682620143, (43, 23718): 2160.5109359088087, (43, 24001): 2286.459494588306, (43, 24094): 2316.503480749865, (43, 24129): 2335.989751529263, (43, 24174): 2293.0747650411317, (43, 24235): 2334.759057493555, (43, 24259): 2354.942607621561, (43, 24260): 2353.308242940533, (43, 24261): 2349.359046460293, (43, 24305): 2377.802021628661, (43, 24306): 2381.246061920013, (43, 24307): 2375.7624083550195, (43, 24308): 2338.904545117974, (43, 24498): 2431.414046498796, (43, 24499): 2431.7328383774507, (43, 24500): 2428.257166204962, (43, 24668): 2409.481170387778, (43, 24711): 2453.349866786749, (43, 24756): 2464.6695896260444, (43, 24788): 2470.9116741029356, (43, 24809): 2447.751778473331, (43, 24813): 2455.1059732699487, (43, 24821): 2452.744646938739, (43, 24825): 2454.260794138356, (43, 24832): 2446.368994531821, (43, 24833): 2449.769247631539, (43, 24835): 2453.085844621593, (43, 24837): 2458.658442933755, (43, 24840): 2445.758680172472, (43, 24841): 2451.185734543966, (43, 24844): 2445.800173388976, (43, 24845): 2449.339017537027, (43, 24846): 2448.4231731780837, (43, 24849): 2450.2221979833394, (43, 24850): 2456.006889177834, (43, 24863): 2409.525364995121, (43, 24866): 2415.6468035606904, (43, 24885): 2422.4788623408626, (43, 24886): 2422.762218607059, (43, 24889): 2436.945576697973, (43, 24903): 2442.46688257121, (43, 24909): 2420.869878617622, (43, 24999): 2684.767952910132, (43, 25019): 2678.3729120055186, (43, 25028): 2681.087220714759, (43, 25137): 2094.1556545791886, (43, 25145): 2101.839017976293, (43, 25208): 2173.5792550379015, (43, 25233): 2162.680251233671, (43, 25371): 2105.693050498396, (43, 25377): 2087.354883062487, (43, 25828): 1710.5383931866659, (43, 25851): 1660.568905481847, (43, 25874): 1712.551743818273, (43, 25898): 1730.2905785462726, (43, 25946): 1705.113630113436, (43, 26047): 1812.490446599401, (43, 26066): 1978.5560338791734, (43, 26197): 1876.3959234317645, (43, 26212): 1504.8093857945694, (43, 26253): 1484.3133374166505, (43, 26254): 1492.2896343282644, (43, 26257): 1498.9311961847511, (43, 26258): 1488.2802530410343, (43, 26260): 1493.795257545154, (43, 26266): 1487.1934860761755, (43, 26267): 1493.532032061812, (43, 26271): 1493.6025171846766, (43, 26304): 1566.6512423951976, (43, 26305): 1566.4897659766593, (43, 26363): 1683.9411532358424, (43, 26441): 1034.4715134813896, (43, 26442): 1034.3917690566084, (43, 26450): 1044.079184826553, (43, 26459): 1053.0691205685564, (43, 26462): 1055.4339152556297, (43, 26467): 1028.9445482037556, (43, 26471): 1032.0228595117649, (43, 26472): 1031.557655784871, (43, 26473): 1030.6554344119388, (43, 26476): 1022.736241907293, (43, 26485): 1044.3824346971971, (43, 26493): 1039.8588660378732, (43, 26524): 1055.2260133518766, (43, 26525): 1053.9439568805765, (43, 26556): 1036.0285180742628, (43, 26560): 1044.0327952724517, (43, 26561): 1051.403314018583, (43, 26564): 1036.5627647387319, (43, 26569): 1050.438645186051, (43, 26570): 1050.018987170933, (43, 26573): 1044.791786020139, (43, 26581): 1041.6777403723904, (43, 26583): 1045.734799148918, (43, 26593): 1037.441683558576, (43, 26837): 1023.6599020656992, (43, 26844): 1019.24457694344, (43, 26863): 1020.713991596537, (43, 26893): 1004.2943163383463, (43, 26902): 997.9271084843582, (43, 26905): 1011.8547557417338, (43, 26912): 1004.5445976518937, (43, 26921): 1013.3359344646699, (43, 26922): 1015.1644627455912, (43, 27212): 1194.702508893351, (43, 27218): 1208.4841439858567, (43, 27239): 1185.9875843099935, (43, 27257): 1186.0657313516283, (43, 27274): 1182.7172486573038, (43, 27279): 1179.7013602831087, (43, 27282): 1183.8720779092127, (43, 27283): 1189.4648520970086, (43, 27285): 1178.608388287896, (43, 27286): 1175.8925010081432, (43, 27290): 1186.8618323794092, (43, 27295): 1194.9724013634766, (43, 27300): 1183.4891827385677, (43, 27344): 1178.0203635204145, (43, 27366): 1169.5598723970356, (43, 27383): 1170.3957516223882, (43, 27398): 1174.5635244115808, (43, 27406): 1181.3557422456818, (43, 27407): 1183.1795789084954, (43, 27426): 1214.0620158260006, (43, 27432): 1223.7234626505667, (43, 27460): 1220.9968332161882, (43, 27523): 1111.6741841103135, (43, 27545): 1107.067335328395, (43, 27602): 1006.0155922923769, (43, 27606): 1010.3073256722263, (43, 27646): 1016.3096753186478, (43, 27667): 994.3590560618555, (43, 27672): 996.2372893667299, (43, 27674): 998.0438098367483, (43, 27688): 1006.8468877578379, (43, 27692): 989.0813236197522, (43, 27693): 991.6672388639292, (43, 27705): 988.4220599741461, (43, 27712): 984.2548131375481, (43, 27786): 1140.114301858879, (43, 27790): 1193.0935490494517, (43, 27791): 1200.3739167065194, (43, 27795): 1139.030844490798, (43, 27801): 1174.2298243071941, (43, 27813): 1133.0721178804977, (43, 27816): 1144.429318531054, (43, 27823): 1175.981954562955, (43, 27830): 1157.6163505343325, (43, 27884): 1022.4752362446037, (43, 27885): 1020.623749083954, (43, 27896): 1022.996674796127, (43, 27919): 1026.2303729192442, (43, 27922): 1021.425355545328, (43, 27930): 1025.8482178120937, (43, 27934): 1023.0294317187407, (43, 27935): 1019.8504168067789, (43, 27948): 844.8265748693431, (43, 27951): 894.3401874889018, (43, 28061): 698.8240253212184, (43, 28290): 418.52211342576635, (43, 28292): 401.1783826164698, (43, 28293): 414.09582339244554, (43, 28295): 407.7849033138394, (43, 28296): 414.3162073113737, (43, 28297): 426.84413946047295, (43, 28302): 420.9146539371826, (43, 28310): 604.695207182476, (43, 28313): 624.7642038253606, (43, 28372): 583.9993790504346, (43, 28398): 586.9261978642203, (43, 28399): 590.0058604801089, (43, 28400): 590.3282401054655, (43, 28401): 584.4677693962336, (43, 28445): 637.5802863477454, (43, 28475): 555.8388033467412, (43, 28885): 2320.3568464456494, (43, 28886): 2316.0203910461687, (43, 28915): 2316.470079056229, (43, 28916): 2314.2400300555664, (43, 28917): 2311.664685759793, (43, 28921): 2327.763028921651, (43, 28931): 2326.053899735482, (43, 28945): 2298.706323873986, (43, 28982): 2306.2075715661144, (43, 29219): 2312.0505228325815, (43, 29228): 2296.4208006427357, (43, 29246): 2390.3437597497364, (43, 29248): 2386.0533696023585, (43, 29282): 2365.9229042546895, (43, 29290): 2403.4894680507255, (43, 29291): 2398.5299720150947, (43, 29292): 2402.7650973348977, (43, 29293): 2394.7452439616163, (43, 29294): 2399.913839337686, (43, 29298): 2394.5981378866336, (43, 29299): 2393.1448194455243, (43, 29304): 2387.343958954806, (43, 29317): 2369.0994713053665, (43, 29323): 2367.768967578869, (43, 29330): 2376.426109172785, (43, 29331): 2381.364227167531, (43, 29344): 2308.0409523032054, (43, 29445): 2116.1395829211324, (43, 29724): 1293.2641571377133, (43, 29738): 1294.6537956034783, (43, 29745): 1294.9932423591447, (43, 29748): 1317.9810670705301, (43, 29750): 1329.5764565881163, (43, 29759): 1313.3739925094753, (43, 29772): 1318.8356478850924, (43, 29781): 1318.2740981735415, (43, 29784): 1307.8210712083128, (43, 29790): 1323.3720710995967, (43, 29811): 1330.0916948874453, (43, 29817): 1397.8886496984217, (43, 29818): 1397.7076809671926, (43, 29929): 1280.6635866021616, (43, 30039): 1237.809191854428, (43, 30066): 1190.0066792126502, (43, 30116): 1192.4574324743105, (43, 30238): 1206.4775584516258, (43, 30248): 1133.1334391451862, (43, 30260): 1127.3133628236576, (43, 30545): 2273.5305308940583, (43, 30733): 2106.0823274353347, (43, 30756): 2048.089036231727, (43, 30921): 2136.1606130396267, (43, 31079): 1752.73968492828, (43, 31149): 1721.998606570314, (43, 31154): 1723.6378815834066, (43, 31160): 1720.4730902845433, (43, 31163): 1720.8233884789313, (43, 31189): 1644.109964627572, (43, 31215): 1649.7205285679145, (43, 31259): 1645.8366608755546, (43, 31262): 1637.2555578029144, (43, 31430): 1763.8952500390255, (43, 31568): 1565.139637636237, (43, 31751): 1715.0346590645663, (44, 109): 708.0736365770441, (44, 872): 2149.3942167969976, (44, 873): 2157.5251071207385, (44, 877): 2154.423857114168, (44, 879): 2155.625161602608, (44, 884): 2147.3420210518807, (44, 889): 2152.462585309971, (44, 891): 2144.6647859919, (44, 892): 2161.9391154990317, (44, 894): 2160.933260016855, (44, 896): 2153.183908593954, (44, 903): 2154.671325742179, (44, 909): 2140.9951593252385, (44, 910): 2144.29971386638, (44, 912): 2138.910456972076, (44, 913): 2132.954231137054, (44, 916): 2130.5053356417056, (44, 926): 2147.031171608215, (44, 927): 2144.312054328257, (44, 948): 2141.7253603467384, (44, 961): 2146.625464037821, (44, 962): 2147.5823588024323, (44, 963): 2148.646978824613, (44, 967): 2158.129946076337, (44, 974): 2153.64916455402, (44, 998): 2161.3063645873867, (44, 1014): 2339.6193565985072, (44, 1086): 2130.736523567509, (44, 1087): 2129.84816229025, (44, 1089): 2122.2646077942204, (44, 1090): 2125.6855697076876, (44, 1092): 2137.421153990119, (44, 1097): 2128.442939722027, (44, 1107): 2143.3488048001536, (44, 1387): 912.286080639242, (44, 1554): 784.8553306380786, (44, 1827): 2519.2847715847765, (44, 1828): 2520.190847357958, (44, 1829): 2521.4111915656276, (44, 1830): 2519.9248834974564, (44, 1831): 2520.690177345593, (44, 1832): 2519.8329952889276, (44, 1833): 2519.965148161893, (44, 1836): 2519.0647325605555, (44, 1841): 2524.2313175662935, (44, 1843): 2522.045854477116, (44, 1844): 2522.9852848730015, (44, 1845): 2520.3536757668535, (44, 1847): 2512.029807354454, (44, 1848): 2514.9180577303127, (44, 1849): 2528.4208888880385, (44, 1850): 2529.8697841468193, (44, 1851): 2517.0386841420896, (44, 1852): 2517.1727069166286, (44, 1854): 2518.61745152725, (44, 1856): 2511.51637343282, (44, 1857): 2514.678423799162, (44, 1858): 2527.1588470539036, (44, 1861): 2521.1618926142237, (44, 1866): 2511.2648169860927, (44, 1867): 2524.4475905322392, (44, 1868): 2522.7564326365664, (44, 1870): 2522.6442264477996, (44, 1871): 2524.1164357502544, (44, 1875): 2518.5232295016826, (44, 1880): 2513.3962089548104, (44, 1882): 2514.140095242404, (44, 1883): 2530.0703372996627, (44, 1889): 2515.037329126151, (44, 1893): 2521.6949953551198, (44, 1894): 2519.666939156247, (44, 1899): 2513.2823576595106, (44, 1900): 2514.81902523608, (44, 1902): 2525.2514967229554, (44, 1905): 2527.8451399022288, (44, 1907): 2516.9667155508964, (44, 1910): 2518.0364622966567, (44, 1917): 2533.6593123295434, (44, 1920): 2517.2325455770488, (44, 1935): 2528.353487215575, (44, 1937): 2530.581463811159, (44, 1946): 2508.8979707604235, (44, 1949): 2511.4592244273117, (44, 1950): 2502.4100354427555, (44, 1951): 2506.736169217509, (44, 1952): 2509.748076379391, (44, 1953): 2511.3143446333124, (44, 1954): 2509.1709958484585, (44, 1958): 2510.662834383972, (44, 1960): 2514.904155801717, (44, 1968): 2516.5783213996406, (44, 1969): 2529.014485245759, (44, 1974): 2525.749879250653, (44, 1975): 2525.670143750508, (44, 1979): 2519.6621251880088, (44, 1980): 2519.0499570809448, (44, 1981): 2520.9157726252406, (44, 1985): 2522.4206420782853, (44, 1994): 2498.652490484872, (44, 2011): 2513.985923222885, (44, 2019): 2535.0803062278037, (44, 2020): 2532.2897590289067, (44, 2029): 2521.5649552231966, (44, 2030): 2530.357651968112, (44, 2032): 2519.7445243377897, (44, 2033): 2525.5069782489827, (44, 2034): 2525.3428337149567, (44, 2036): 2514.369119201656, (44, 2037): 2517.188424848716, (44, 2038): 2518.41804401552, (44, 2042): 2550.800283718566, (44, 2050): 2524.1437449836126, (44, 2051): 2523.606011212002, (44, 2053): 2524.4965203602133, (44, 2054): 2527.359315299022, (44, 2066): 2521.5211025569856, (44, 2067): 2521.575764807165, (44, 2071): 2493.281453702318, (44, 2072): 2498.7047700830512, (44, 2073): 2484.1216284005354, (44, 2074): 2483.352354118709, (44, 2080): 2474.1693377064676, (44, 2082): 2501.614610474322, (44, 2083): 2504.4229213823864, (44, 2089): 2498.565345727392, (44, 2090): 2501.1956141293986, (44, 2092): 2497.689265767165, (44, 2098): 2477.72352680214, (44, 2099): 2480.8210899203873, (44, 2101): 2477.1063067316236, (44, 2102): 2491.8521389810753, (44, 2103): 2487.1950855177433, (44, 2104): 2484.6242311800142, (44, 2106): 2506.2783077794575, (44, 2112): 2479.019922345249, (44, 2113): 2493.9202187760725, (44, 2114): 2497.3877913658803, (44, 2117): 2508.446072341134, (44, 2123): 2488.667911680597, (44, 2124): 2491.7077888831177, (44, 2134): 2482.9596433277497, (44, 2138): 2491.938817024, (44, 2141): 2484.039764042779, (44, 2148): 2488.1416036958585, (44, 2150): 2476.6250548160247, (44, 2151): 2479.7999500486367, (44, 2152): 2474.921404749674, (44, 2153): 2489.201842850841, (44, 2154): 2476.6285753795596, (44, 2155): 2475.1182970052755, (44, 2156): 2472.8179077222876, (44, 2157): 2475.7901527801605, (44, 2160): 2496.0274181785976, (44, 2161): 2474.363655376839, (44, 2162): 2489.595483450837, (44, 2163): 2485.3370810713227, (44, 2164): 2485.029095117538, (44, 2168): 2477.6807196127784, (44, 2172): 2480.360179828106, (44, 2174): 2479.39015584047, (44, 2178): 2482.8069773188904, (44, 2179): 2480.8271612291296, (44, 2183): 2491.693074203538, (44, 2185): 2491.8642790188082, (44, 2186): 2489.448511953756, (44, 2190): 2496.6598171316427, (44, 2192): 2492.303011712529, (44, 2193): 2492.5566018685827, (44, 2194): 2488.1060735126066, (44, 2195): 2487.419181761818, (44, 2197): 2493.235753130536, (44, 2205): 2486.9463727718726, (44, 2207): 2478.7750491314864, (44, 2208): 2483.3366248471284, (44, 2212): 2493.949958424019, (44, 2214): 2403.3057944965217, (44, 2225): 2413.838944915864, (44, 2231): 2393.810103713361, (44, 2278): 2457.792136586904, (44, 2284): 2466.855547837476, (44, 2285): 2465.53499584644, (44, 2291): 2447.0734529062997, (44, 2292): 2449.3864294860787, (44, 2307): 2460.8930058996207, (44, 2313): 2444.816207373631, (44, 2317): 2442.750663869088, (44, 2319): 2452.5058295403655, (44, 2321): 2456.65706937821, (44, 2323): 2456.196572174548, (44, 2326): 2472.3888714852587, (44, 2327): 2468.4234698087225, (44, 2329): 2465.707221704512, (44, 2330): 2462.59074834841, (44, 2332): 2469.0792419907248, (44, 2344): 2459.102150267039, (44, 2346): 2458.851618680909, (44, 2361): 2457.847127081554, (44, 2368): 2503.797848094639, (44, 2374): 2508.112130595442, (44, 2375): 2509.6047816413247, (44, 2377): 2494.416335964361, (44, 2378): 2512.325658952323, (44, 2379): 2512.642918905419, (44, 2380): 2514.1948482494754, (44, 2383): 2498.5205778771697, (44, 2385): 2500.8957207417443, (44, 2395): 2501.215347956501, (44, 2397): 2510.801294379475, (44, 2398): 2489.570260676617, (44, 2399): 2495.0809973651853, (44, 2400): 2493.8534361473967, (44, 2402): 2502.365988734383, (44, 2403): 2505.7653675508727, (44, 2404): 2506.669390793315, (44, 2405): 2498.4515973495313, (44, 2407): 2505.187056500778, (44, 2408): 2509.147174188692, (44, 2409): 2500.955130861423, (44, 2411): 2505.6236093495118, (44, 2412): 2504.7756916183525, (44, 2413): 2507.5484381037545, (44, 2414): 2502.998248521591, (44, 2422): 2504.5470507571, (44, 2424): 2505.7611109828226, (44, 2426): 2506.5215861461065, (44, 2433): 2500.13770408768, (44, 2436): 2498.373719909577, (44, 2437): 2478.541584227049, (44, 2440): 2482.93364367988, (44, 2445): 2570.051279515523, (44, 2447): 2559.333897186626, (44, 2454): 2569.5005061629045, (44, 2455): 2570.135052971018, (44, 2460): 2538.4726612782197, (44, 2461): 2542.36541511909, (44, 2471): 2604.9620368312726, (44, 2492): 2534.842587899319, (44, 2511): 2503.8328329935543, (44, 2523): 2519.6804872913185, (44, 2525): 2514.710162460588, (44, 2535): 2524.8854145939704, (44, 2537): 2517.8395395449706, (44, 2538): 2522.7991744611727, (44, 2539): 2520.2692003423845, (44, 2540): 2528.069499354343, (44, 2542): 2533.001015039451, (44, 2559): 2633.5192667428414, (44, 2575): 2623.9384539711214, (44, 2599): 2474.6278700501207, (44, 2600): 2508.039604348308, (44, 2607): 2489.0999172627817, (44, 2627): 2521.4540171102553, (44, 2647): 2539.5837657384177, (44, 2674): 2530.6697021008827, (44, 2681): 2527.810560150661, (44, 2683): 2536.9700238516975, (44, 2686): 2526.740659481465, (44, 2689): 2646.9499413940075, (44, 2690): 2647.466672582621, (44, 2713): 2668.7540068495346, (44, 2714): 2670.5143212641465, (44, 2715): 2673.4932278076667, (44, 2739): 2670.929523744719, (44, 2740): 2652.879340479735, (44, 2741): 2654.4133032729433, (44, 2749): 2666.5360025931905, (44, 2750): 2667.561440505591, (44, 2752): 2669.728346187487, (44, 2755): 2672.0244063096975, (44, 2758): 2671.257836186376, (44, 2759): 2671.310356376679, (44, 2769): 2667.95737708825, (44, 2771): 2657.4958140905774, (44, 2779): 2657.744600577008, (44, 2784): 2623.922140595729, (44, 2800): 2629.2539624162405, (44, 2802): 2646.752233432184, (44, 2803): 2645.702850109948, (44, 2804): 2643.745811958697, (44, 2805): 2649.0089115621836, (44, 2807): 2648.907418114455, (44, 2809): 2647.610418623416, (44, 2812): 2628.7096156443336, (44, 2814): 2646.047094527573, (44, 2817): 2645.951759401008, (44, 2819): 2649.5025040324194, (44, 2823): 2629.8388645606765, (44, 2832): 2652.5904121803196, (44, 2836): 2639.1880540338047, (44, 2839): 2648.950102936459, (44, 2841): 2646.9951288894704, (44, 2843): 2646.1337853961068, (44, 2846): 2641.492500469599, (44, 2849): 2654.5390953431756, (44, 2852): 2651.5494721068326, (44, 2853): 2655.909970561079, (44, 2876): 2656.8715102648525, (44, 2877): 2667.5650989667943, (44, 2885): 2670.013352013845, (44, 2918): 2651.5555621978942, (44, 2921): 2656.082593834525, (44, 2925): 2635.0886317957256, (44, 2926): 2628.218453557121, (44, 2930): 2643.295729350912, (44, 2931): 2636.868226450219, (44, 2938): 2651.472357760854, (44, 2940): 2665.568357375956, (44, 2947): 2649.9468677801624, (44, 2949): 2643.4784089246346, (44, 2950): 2645.419401546063, (44, 2952): 2643.132529782186, (44, 2958): 2642.744362405985, (44, 2959): 2645.104398307733, (44, 2960): 2650.135957448875, (44, 2961): 2647.631562831157, (44, 2963): 2640.730545768258, (44, 2968): 2642.1013000213993, (44, 2976): 2640.2068728048102, (44, 2981): 2595.777919580121, (44, 2982): 2594.36352473149, (44, 2984): 2592.0657151209007, (44, 3003): 2587.9157821855783, (44, 3046): 2560.1360841341807, (44, 3050): 2582.5368329791518, (44, 3051): 2584.3852019758124, (44, 3053): 2579.330087371032, (44, 3069): 2606.9507030768877, (44, 3071): 2578.4863486265226, (44, 3080): 2669.7988461390223, (44, 3199): 2579.570827206514, (44, 3200): 2574.195226580121, (44, 3205): 2606.775328372131, (44, 3209): 2576.9324095264083, (44, 3215): 2574.604204717929, (44, 3217): 2568.091194290769, (44, 3249): 2575.2836176213887, (44, 3263): 2624.4977330581023, (44, 3289): 2591.049252933949, (44, 3301): 2592.401922421269, (44, 3302): 2590.1328862190962, (44, 3307): 2587.231097552456, (44, 3310): 2595.2052613414194, (44, 3391): 2597.1279733866695, (44, 3509): 1548.3428982602904, (44, 3510): 1543.7112546553055, (44, 3511): 1546.9334253416846, (44, 3512): 1544.1893205607446, (44, 3514): 1545.2725179005827, (44, 3519): 1558.5480995491794, (44, 3536): 1556.7557117780123, (44, 3545): 1564.1628263931846, (44, 3548): 1557.241596031541, (44, 3572): 1559.2193788804118, (44, 3581): 1553.1553521475796, (44, 3583): 1550.561777545705, (44, 3601): 1567.0449344620736, (44, 3656): 1559.0290439224173, (44, 3669): 1548.9395817877128, (44, 3670): 1553.053643892262, (44, 3695): 1529.7313015568463, (44, 3696): 1533.0327502887465, (44, 3782): 1561.4057664613224, (44, 3792): 1555.9281890949085, (44, 3989): 442.22588313861206, (44, 4008): 467.9775170346626, (44, 4031): 469.0471683903322, (44, 4045): 457.2831437704827, (44, 4144): 456.54603723344445, (44, 4145): 429.0989172003722, (44, 4164): 446.16784917278676, (44, 4168): 437.35466237348464, (44, 4173): 435.3640288538493, (44, 4181): 419.8207779764235, (44, 4228): 406.8388305671087, (44, 4248): 398.34440585095444, (44, 4254): 271.8663601635715, (44, 4260): 270.2886747896634, (44, 4262): 279.46678135682635, (44, 4273): 276.52905102136094, (44, 4319): 225.43793386216717, (44, 4326): 222.643189155713, (44, 4328): 222.15876031032428, (44, 4334): 228.94585403794935, (44, 4335): 228.45160953053005, (44, 4372): 847.6529659246609, (44, 4413): 914.5860374132143, (44, 4434): 840.5931615941, (44, 4447): 831.3170807891969, (44, 4452): 843.6956670008345, (44, 4463): 863.8271252688767, (44, 4465): 859.774947299124, (44, 4619): 967.9215386127167, (44, 4645): 967.2047370340509, (44, 4657): 972.0755084756644, (44, 4666): 974.7990642435752, (44, 4676): 979.2949622162789, (44, 4678): 977.5163492048723, (44, 4689): 981.4429448523349, (44, 4704): 1006.1804786502648, (44, 4726): 1193.4555284427731, (44, 4727): 1190.494514736316, (44, 4730): 1184.389301970409, (44, 4731): 1188.5509841269215, (44, 4734): 1178.0138153127868, (44, 4735): 1177.2791450687007, (44, 4736): 1180.4960669316522, (44, 4737): 1177.969299297016, (44, 4738): 1180.0899643573912, (44, 4756): 1184.1544974921055, (44, 4760): 1159.1518914296225, (44, 4761): 1156.7432925711485, (44, 4762): 1157.5907611853386, (44, 4765): 1161.8286920453993, (44, 4773): 1197.2807907971896, (44, 4774): 1197.9313280709107, (44, 4790): 1194.8193044164695, (44, 4795): 1191.4078142621831, (44, 4799): 1200.9535173832282, (44, 4801): 1211.645266664873, (44, 4804): 1188.2933729621575, (44, 4805): 1185.5369732132494, (44, 4806): 1201.6633974507965, (44, 4815): 1201.7314125579655, (44, 4816): 1207.6315464108175, (44, 4817): 1212.8788559689121, (44, 4826): 1207.310908932854, (44, 4830): 1204.7372766198903, (44, 4839): 1167.954309416144, (44, 4840): 1172.2312549196818, (44, 4841): 1167.3357575056027, (44, 4846): 1164.6424220583422, (44, 4848): 1167.2760506925185, (44, 4850): 1170.519617465381, (44, 4871): 1121.1515129495708, (44, 4883): 1151.0087935961303, (44, 4900): 1130.9777807202731, (44, 4901): 1129.962803165986, (44, 4917): 1035.5032232002577, (44, 4931): 1020.0861536088773, (44, 4944): 1034.6812976446197, (44, 4956): 1025.4879143266228, (44, 4958): 1030.1712967680735, (44, 4959): 1030.7888393092, (44, 4961): 1026.5045271924378, (44, 4966): 1024.724414053376, (44, 5207): 1008.5096270851749, (44, 5272): 588.8930755750874, (44, 5283): 593.9471317588775, (44, 5287): 616.2351341057873, (44, 5289): 619.0543803198397, (44, 5293): 575.951954314656, (44, 5295): 588.3586895433424, (44, 5296): 596.8709410536685, (44, 5298): 601.5126996506624, (44, 5303): 612.6245517002229, (44, 5305): 603.1458150100564, (44, 5306): 612.0592348403914, (44, 5307): 601.6704809606503, (44, 5308): 607.9322953780879, (44, 5313): 596.8758381367771, (44, 5314): 596.3608681437158, (44, 5317): 613.5790323206595, (44, 5319): 610.3052008145157, (44, 5324): 601.1935958881056, (44, 5326): 594.8328488848972, (44, 5348): 618.4975727117409, (44, 5351): 633.6597478499489, (44, 5399): 634.1340422130011, (44, 5413): 658.0752303112322, (44, 5422): 628.1067031959344, (44, 5445): 621.7009662564225, (44, 5448): 617.7201345317495, (44, 5456): 625.890688472503, (44, 5467): 631.979939731505, (44, 5624): 563.7868423688221, (44, 5671): 591.9811823205067, (44, 5672): 583.1454681095049, (44, 5797): 696.7646265349523, (44, 5871): 776.9792350399118, (44, 5976): 727.4702476814547, (44, 6118): 2103.047754846716, (44, 6248): 2201.9756525592497, (44, 6345): 508.4658322790852, (44, 6352): 531.4024773872289, (44, 6354): 502.4938226452425, (44, 6359): 498.64244878726186, (44, 6376): 529.6609076745318, (44, 6378): 505.2807967890912, (44, 6381): 501.00440140489974, (44, 6383): 513.0496524225991, (44, 6396): 506.76957844185495, (44, 6399): 509.03571383201194, (44, 6408): 529.8548412836432, (44, 6409): 517.4283429981086, (44, 6419): 551.8075100281955, (44, 6422): 525.4885272775767, (44, 6423): 527.2375616310848, (44, 6424): 502.9354633244827, (44, 6439): 506.82478694502475, (44, 6464): 512.6647625215855, (44, 6465): 515.4126335691735, (44, 6469): 513.7027879109845, (44, 6470): 515.3789962950624, (44, 6472): 491.1487037543862, (44, 6480): 493.19419406557, (44, 6486): 477.823315810486, (44, 6497): 482.7487752717939, (44, 6503): 508.88818913208434, (44, 6508): 508.4139908937355, (44, 6509): 503.54169151866955, (44, 6521): 489.38488256027387, (44, 6544): 489.776385892109, (44, 6552): 519.0459151558763, (44, 6553): 522.4101034641242, (44, 6554): 525.8500656485874, (44, 6578): 513.6149549327753, (44, 6582): 514.8978022912919, (44, 6601): 511.7822562888576, (44, 6609): 485.9685136043937, (44, 6610): 484.64389378482264, (44, 6611): 484.9067299466569, (44, 6614): 487.3008728086833, (44, 6615): 486.3080594280101, (44, 6616): 481.49699701838927, (44, 6617): 483.48099045261154, (44, 6618): 477.28942781224555, (44, 6619): 489.5845030703354, (44, 6620): 480.892537005833, (44, 6621): 483.70717024806953, (44, 6622): 483.38261152249277, (44, 6623): 486.9244366118558, (44, 6624): 488.90739827351865, (44, 6625): 489.77024652131973, (44, 6626): 490.03154273514684, (44, 6627): 488.6058532591551, (44, 6628): 480.9975052640956, (44, 6629): 487.42241577137895, (44, 6630): 493.28561485557265, (44, 6632): 488.01899466364875, (44, 6634): 496.0350247319662, (44, 6635): 485.03507810782787, (44, 6636): 481.1444655464409, (44, 6637): 491.3756865310885, (44, 6638): 492.32218969874685, (44, 6639): 487.90920795205784, (44, 6640): 492.1476106818395, (44, 6641): 483.3992378073949, (44, 6642): 491.85069411410444, (44, 6643): 490.84125005932077, (44, 6645): 488.8875665077581, (44, 6646): 478.7414618024992, (44, 6647): 491.1911502846349, (44, 6653): 486.6368690899804, (44, 6655): 488.0935360895485, (44, 6658): 496.0084568440099, (44, 6662): 491.6047766012931, (44, 6819): 653.1951425117251, (44, 6996): 597.7148734416803, (44, 7059): 559.4686543169153, (44, 7187): 651.2289711945793, (44, 7304): 711.8278293593254, (44, 7528): 608.5007413938786, (44, 7720): 377.84201588287704, (44, 7793): 387.7265570741244, (44, 7807): 382.82684849672233, (44, 7808): 390.2555173656611, (44, 7831): 461.67920424091534, (44, 7850): 426.69231517428943, (44, 7852): 435.9368361723242, (44, 8012): 383.6833504539221, (44, 8125): 409.620639669478, (44, 8208): 311.7726327005834, (44, 8392): 434.43996622799676, (44, 8651): 839.2364422255799, (44, 9088): 676.0628820924413, (44, 9443): 943.0738347287667, (44, 9444): 938.3742546228927, (44, 9828): 1126.4326284212714, (44, 9868): 1114.0767559605306, (44, 10180): 413.0957009952247, (44, 10256): 352.4117227472229, (44, 10276): 365.0782638285355, (44, 10378): 318.07632397824665, (44, 10676): 499.9036537507855, (44, 10714): 561.3525534198889, (44, 10730): 507.65130865198904, (44, 10862): 1091.5225982437566, (44, 10881): 1090.9501161499288, (44, 10883): 1093.3944718843013, (44, 10885): 1091.0698996800613, (44, 10891): 1097.2589704328634, (44, 10909): 1091.6180323393762, (44, 10911): 1085.6972552855325, (44, 10913): 1087.7131408693315, (44, 10915): 1084.7069909841355, (44, 10919): 1082.0962702352087, (44, 11037): 1160.2159042137068, (44, 11039): 1139.5171899850209, (44, 11516): 756.415487458716, (44, 11856): 231.10659343966063, (44, 11857): 233.4235994616373, (44, 11861): 232.43600468513435, (44, 11881): 222.00674023001173, (44, 11902): 206.79534605421748, (44, 11911): 198.96507710903282, (44, 11914): 203.25716259156252, (44, 11922): 216.3519680484581, (44, 11924): 218.7345363441486, (44, 11926): 214.00319025140215, (44, 11950): 217.9330333198931, (44, 11963): 233.54422571446202, (44, 11983): 216.38974415759745, (44, 11985): 241.76673714133887, (44, 12009): 233.01601165220387, (44, 12010): 223.1644882231166, (44, 12018): 224.24980420077102, (44, 12020): 228.08092397626572, (44, 12021): 229.32082428250826, (44, 12024): 240.00323907372427, (44, 12025): 237.50687140525224, (44, 12027): 234.70223281250492, (44, 12031): 221.33580816495714, (44, 12032): 225.94198969725986, (44, 12035): 231.1117031923048, (44, 12041): 246.8500464898591, (44, 12045): 99.97896327451589, (44, 12145): 155.00956898801977, (44, 12275): 459.81519570385393, (44, 12294): 439.82984711176925, (44, 12358): 527.3109898149606, (44, 12463): 565.4609514397035, (44, 12465): 564.8950159323948, (44, 12482): 573.4432858232702, (44, 12503): 572.7940682087984, (44, 12506): 576.472499807664, (44, 12549): 562.487530501783, (44, 12559): 560.8170872488347, (44, 12569): 565.9731642440001, (44, 12572): 568.6287296359143, (44, 12574): 562.4134739060977, (44, 12576): 565.041342127789, (44, 12591): 561.2180695393208, (44, 12608): 582.0707410862664, (44, 12696): 543.3021515979151, (44, 12710): 561.4530931356193, (44, 12728): 554.6036352845834, (44, 12766): 255.33298801596396, (44, 12771): 245.84130421727667, (44, 12790): 249.74663540622666, (44, 12795): 262.03564452790397, (44, 12797): 277.33371134605056, (44, 12798): 272.16460006678807, (44, 12811): 249.26986354120993, (44, 12830): 261.19056793610315, (44, 12848): 248.25719792130417, (44, 12850): 241.06373331366007, (44, 12852): 259.54778976053416, (44, 12854): 263.10639553419225, (44, 12859): 242.3717762789101, (44, 12861): 266.1930542411423, (44, 12865): 249.29382980466792, (44, 12866): 248.19974129234143, (44, 12867): 244.12770281131674, (44, 12874): 246.44871063220285, (44, 12875): 242.72542792240756, (44, 12881): 256.3371431198685, (44, 12883): 251.84777156405102, (44, 12885): 241.24245651775342, (44, 12888): 251.93253682826278, (44, 12889): 251.09099682668327, (44, 12892): 246.8461057360207, (44, 12893): 253.69489166140642, (44, 12896): 249.72809847308062, (44, 12906): 255.13583403526394, (44, 13018): 337.8639916782287, (44, 13071): 350.21380780890445, (44, 13131): 331.4406134606958, (44, 13146): 298.29089601263513, (44, 13159): 387.6920449960947, (44, 13193): 333.4662026907219, (44, 13198): 366.9569152004454, (44, 13292): 307.0011140894719, (44, 13296): 276.7941328160446, (44, 13406): 419.15341255014147, (44, 13407): 422.5615615285064, (44, 13417): 441.3284274894194, (44, 13418): 438.90817547192967, (44, 13438): 405.8272103572466, (44, 13442): 396.4625689028651, (44, 13443): 401.1385452280899, (44, 13764): 869.3660184603565, (44, 13766): 863.595833384712, (44, 13771): 874.3354206389346, (44, 13783): 865.8972614022864, (44, 13784): 855.1123762766182, (44, 13792): 893.2207296963246, (44, 13824): 870.8621198228586, (44, 14017): 809.324212880945, (44, 14870): 970.1794749722088, (44, 14997): 681.2452066581521, (44, 15000): 681.8334698729433, (44, 15003): 679.181855855054, (44, 15006): 665.4015085919075, (44, 15007): 661.5736257398238, (44, 15056): 665.5390048506976, (44, 15063): 669.74488352506, (44, 15069): 672.4782465616483, (44, 15076): 661.7337405818982, (44, 15086): 672.7299114344883, (44, 15087): 678.460170094655, (44, 15111): 689.2747618189949, (44, 15116): 683.1559198677772, (44, 15722): 787.8546706726019, (44, 15998): 888.6816721201449, (44, 16073): 1745.7178721073576, (44, 16939): 2258.6193133678976, (44, 16940): 2252.6475183532884, (44, 16951): 2259.1493594541157, (44, 16963): 2259.7966193885213, (44, 16965): 2267.1953920196306, (44, 16969): 2265.2451878603742, (44, 16970): 2262.5326067203873, (44, 16971): 2255.876919668673, (44, 16973): 2255.3246809362295, (44, 16974): 2270.0681368175824, (44, 16976): 2263.115537270213, (44, 16978): 2258.2899642283437, (44, 16980): 2265.665454829864, (44, 16982): 2269.906220925591, (44, 17045): 2465.113100738415, (44, 17048): 2473.638438367087, (44, 17304): 361.2108637391383, (44, 17305): 357.489958415142, (44, 17330): 361.3173888118996, (44, 17334): 352.91787547620874, (44, 17343): 367.6118930278091, (44, 17345): 353.0936983772199, (44, 17347): 361.20141638501366, (44, 17351): 341.73425395141817, (44, 17372): 352.13988212033604, (44, 17373): 367.0321387245805, (44, 17377): 368.1321194858882, (44, 17382): 358.5333860608185, (44, 17383): 360.13108041225473, (44, 17389): 354.51370827258364, (44, 17400): 364.19033015033796, (44, 17401): 363.926136973539, (44, 17402): 364.80605906694484, (44, 17403): 365.8057799499741, (44, 17440): 354.58238399350194, (44, 17455): 366.42868042867286, (44, 17491): 368.0729716234701, (44, 17507): 347.4760015196512, (44, 17509): 352.8918376693298, (44, 17590): 338.7213508517349, (44, 17615): 313.18214588008397, (44, 17642): 317.4609659801647, (44, 17643): 316.3906043011223, (44, 17668): 313.45114223295656, (44, 17721): 306.95059656351305, (44, 17754): 356.365840772509, (44, 17769): 350.0783666426384, (44, 17776): 327.8711159905545, (44, 17804): 358.7855631770817, (44, 17809): 364.06423470942565, (44, 17824): 361.31048072477455, (44, 17837): 343.87229457060937, (44, 17838): 344.3931376559359, (44, 17862): 340.44420265771623, (44, 17866): 351.76499225418513, (44, 17872): 336.61415107661384, (44, 17873): 327.9596239919256, (44, 17881): 341.2434546456923, (44, 17947): 1770.79769341011, (44, 17951): 1759.3386505133603, (44, 17953): 1757.1576849913154, (44, 17954): 1757.9653215041485, (44, 17959): 1768.4290581215764, (44, 17963): 1764.3793701565055, (44, 18000): 1706.1289082232402, (44, 18001): 1708.4289429103044, (44, 18111): 1872.84326788965, (44, 18148): 1580.3899294612709, (44, 18166): 1694.0407108749898, (44, 18189): 1799.0651522023315, (44, 18239): 369.54193900341875, (44, 18240): 369.5029898201148, (44, 18245): 370.0535975848776, (44, 18247): 368.91317689408163, (44, 18251): 370.06670432163304, (44, 18256): 371.3556454628071, (44, 18258): 370.03559620753106, (44, 18259): 370.2980194701208, (44, 18260): 370.8499309934039, (44, 18262): 371.8709800086119, (44, 18263): 371.728235911922, (44, 18264): 372.2729225671728, (44, 18266): 372.31103673927225, (44, 18267): 372.84481471506086, (44, 18268): 373.12764876607645, (44, 18269): 374.20403634345473, (44, 18275): 373.6957591050817, (44, 18285): 372.07220269775314, (44, 18308): 361.31135172125784, (44, 18313): 357.74078220896365, (44, 18314): 359.33300899691386, (44, 18315): 374.0022003659905, (44, 18316): 373.9821067745541, (44, 18317): 374.48864946899124, (44, 18320): 374.8633026428868, (44, 18321): 375.17209184547, (44, 18322): 375.9564857186989, (44, 18324): 376.4924214692063, (44, 18325): 378.82877279761294, (44, 18326): 377.95505330483013, (44, 18327): 375.02070146484266, (44, 18329): 379.8030408315608, (44, 18330): 378.86468809068367, (44, 18331): 377.25803459680185, (44, 18332): 375.64623975517986, (44, 18333): 378.54832102663397, (44, 18336): 377.1287701494212, (44, 18337): 377.88095748406505, (44, 18403): 377.15646446961244, (44, 18432): 350.51579532398665, (44, 18451): 368.07430251647986, (44, 18466): 387.103873756393, (44, 18481): 374.46260193904914, (44, 18483): 374.49738556481134, (44, 18484): 373.18804590278285, (44, 18485): 369.24596357396894, (44, 18486): 372.61286766290164, (44, 18487): 369.6400183107673, (44, 18489): 372.31345010811634, (44, 18490): 375.2266448781262, (44, 18491): 376.6240093101395, (44, 18492): 366.66516561562827, (44, 18493): 372.106047465534, (44, 18494): 371.7640846709866, (44, 18495): 374.18336335665947, (44, 18496): 372.7315034528748, (44, 18497): 368.95556523162145, (44, 18498): 369.6675004778429, (44, 18499): 371.8506900667909, (44, 18501): 370.2470327237923, (44, 18502): 368.85355544320294, (44, 18503): 367.7953537914542, (44, 18504): 373.3335827186652, (44, 18506): 370.43988135762385, (44, 18507): 369.1192130288812, (44, 18508): 371.5304408218986, (44, 18509): 371.5458034288424, (44, 18510): 367.8196643887381, (44, 18511): 372.516752376305, (44, 18512): 370.88241571723324, (44, 18515): 373.43849963773437, (44, 18516): 373.5109267159019, (44, 18517): 371.7553823695818, (44, 18518): 374.66646089254203, (44, 18519): 373.6494313090567, (44, 18520): 371.137894912093, (44, 18522): 379.67069079434845, (44, 18523): 379.93374050820603, (44, 18532): 381.825708782342, (44, 18535): 377.8560632885573, (44, 18537): 375.6471470152226, (44, 18539): 376.08769156671525, (44, 18540): 376.32377650156593, (44, 18541): 377.3961548810572, (44, 18542): 378.08117390702284, (44, 18543): 374.6670395961059, (44, 18546): 376.2329101938665, (44, 18555): 379.70404344393893, (44, 18556): 380.3197886390693, (44, 18565): 381.52154527887535, (44, 18567): 382.4808968735081, (44, 18568): 380.6091793397087, (44, 18577): 394.21228284234326, (44, 18583): 391.9977641035978, (44, 18605): 394.97205921898546, (44, 18608): 383.59315571862555, (44, 18616): 407.62904205613125, (44, 18618): 418.38910445132217, (44, 18625): 414.9372138483629, (44, 18645): 405.6298864216481, (44, 18646): 407.9496872287919, (44, 18653): 398.6402486880169, (44, 18654): 407.31706403606916, (44, 18655): 401.56580062818006, (44, 18666): 437.0605373616802, (44, 18837): 428.5417399477178, (44, 18974): 372.1916137068062, (44, 18999): 383.89618662634206, (44, 19000): 387.03674372050034, (44, 19174): 286.921275682551, (44, 19342): 352.37063262472157, (44, 19455): 273.44065631894875, (44, 19555): 196.2419306704783, (44, 19564): 231.97254226776437, (44, 19573): 222.59299031363446, (44, 19586): 216.31279118193453, (44, 19605): 212.0241006271876, (44, 19611): 217.16818205420114, (44, 19614): 206.04385778923688, (44, 19641): 262.26130082089196, (44, 19702): 269.95807713536345, (44, 19713): 263.63695562570825, (44, 19731): 138.78457538674323, (44, 19819): 265.21855976315896, (44, 19893): 352.74710355842797, (44, 19899): 393.08701838322656, (44, 19929): 355.2115623986345, (44, 19951): 411.7319981112064, (44, 19962): 374.3789279821776, (44, 19970): 355.8304434606048, (44, 19971): 363.0318160169705, (44, 19972): 363.58590399918916, (44, 19975): 356.5882332687873, (44, 19978): 394.8218925761674, (44, 19987): 391.5092222376149, (44, 19989): 374.50056082450095, (44, 20039): 392.5733332427953, (44, 20043): 393.9040794233416, (44, 20047): 382.97837316176617, (44, 20052): 368.7797100847845, (44, 20054): 373.1441053936738, (44, 20085): 426.6703662846663, (44, 20104): 431.60881762812807, (44, 20132): 407.7536208129429, (44, 20203): 415.35302362082206, (44, 20280): 431.4748993146073, (44, 20285): 439.0854539206762, (44, 20290): 429.37745750260143, (44, 20297): 423.96726905956535, (44, 20309): 445.56893283711497, (44, 20453): 492.81971342461685, (44, 20485): 394.54135620954776, (44, 20520): 382.253657291867, (44, 20526): 401.55546206776756, (44, 20698): 1118.1339964172405, (44, 20868): 1327.0342167408628, (44, 21042): 201.0574576362692, (44, 21057): 156.77145574291586, (44, 21066): 180.89051019139086, (44, 21075): 185.8882598268768, (44, 21093): 201.12333608705475, (44, 21098): 176.8008481733891, (44, 21127): 199.12016515642918, (44, 21130): 192.5980076454836, (44, 21144): 190.56263745483275, (44, 21146): 201.9863659406425, (44, 21147): 190.4687555691171, (44, 21148): 183.7895542772718, (44, 21153): 196.57016874123323, (44, 21293): 133.25266265441653, (44, 21426): 151.66390344579904, (44, 21442): 133.2072329173406, (44, 21451): 132.08570674683043, (44, 21466): 136.41531285630063, (44, 21469): 130.0524273960898, (44, 21471): 139.80944314797043, (44, 21473): 133.69592325742767, (44, 21475): 138.26980174234257, (44, 21482): 129.00737354537614, (44, 21484): 128.74498992488407, (44, 21488): 133.21161182936316, (44, 21494): 134.70536520221913, (44, 21498): 130.7564954553598, (44, 21500): 134.42621577271865, (44, 21514): 111.50656584078853, (44, 21537): 129.2559730088305, (44, 21662): 100.45738727379432, (44, 21691): 126.7096383141415, (44, 21757): 186.9424465639087, (44, 21777): 297.5184957697008, (44, 21778): 303.925678524714, (44, 21779): 302.55432292360115, (44, 21790): 287.9914126734286, (44, 21802): 292.6504497126247, (44, 21824): 288.49039897731586, (44, 21874): 303.79036119335916, (44, 21879): 312.0824358253339, (44, 21983): 263.8515914005864, (44, 22002): 211.0496217099775, (44, 22132): 232.27171510349902, (44, 22261): 1208.9145061504644, (44, 22298): 1197.5021823576124, (44, 22339): 1283.8554069104014, (44, 22508): 1074.666241594333, (44, 22841): 2558.3294217567877, (44, 22842): 2558.617549261038, (44, 22874): 2542.9930413279044, (44, 22941): 2543.816975843833, (44, 22956): 2554.11269670225, (44, 22960): 2556.47318137414, (44, 22968): 2569.820327229158, (44, 22970): 2572.104416304952, (44, 22974): 2579.145798159852, (44, 22980): 2591.2730358086933, (44, 23025): 2592.910121059606, (44, 23028): 2590.77714949387, (44, 23081): 2614.527066510314, (44, 23104): 2597.0366456610423, (44, 23147): 2482.4133344838797, (44, 23298): 16.503635041033082, (44, 23376): 8.080563577899888, (44, 23381): 30.59310980364451, (44, 23529): 29.397925060409666, (44, 23556): 18.719736921186993, (44, 23718): 31.42873529774459, (44, 24001): 133.04079078635692, (44, 24094): 165.4832989168229, (44, 24129): 184.56006949899222, (44, 24174): 148.5610599736559, (44, 24235): 192.0490981833579, (44, 24259): 207.35460381850405, (44, 24260): 206.29760824063004, (44, 24261): 202.0018797270293, (44, 24305): 228.29750295508975, (44, 24306): 232.21427394133198, (44, 24307): 226.53907086990495, (44, 24308): 191.09021129585193, (44, 24498): 277.1438213230696, (44, 24499): 277.48647161821566, (44, 24500): 273.987079481345, (44, 24668): 258.74223953854244, (44, 24711): 300.32826919570556, (44, 24756): 313.72390328080616, (44, 24788): 318.90617469301117, (44, 24809): 298.77175649424004, (44, 24813): 304.77350804669015, (44, 24821): 302.71327865278136, (44, 24825): 304.51350337173994, (44, 24832): 297.1900840215981, (44, 24833): 300.35238187764395, (44, 24835): 303.60210519627003, (44, 24837): 308.4597601112204, (44, 24840): 296.825464886393, (44, 24841): 301.4694771515372, (44, 24844): 297.143653683848, (44, 24845): 299.3975189459935, (44, 24846): 300.02110495822376, (44, 24849): 301.8195813269138, (44, 24850): 305.90988668539484, (44, 24863): 260.7860190259911, (44, 24866): 266.3245552584155, (44, 24885): 273.58279418353146, (44, 24886): 274.4844845275515, (44, 24889): 285.6949621456047, (44, 24903): 290.2820649976081, (44, 24909): 268.70588805516246, (44, 24999): 537.0256053322274, (44, 25019): 532.3335592773913, (44, 25028): 532.7930359489363, (44, 25137): 524.2217844558406, (44, 25145): 524.0793363283332, (44, 25208): 606.7396540175523, (44, 25233): 607.7755965687804, (44, 25371): 472.6986270878215, (44, 25377): 457.03405392115803, (44, 25828): 559.6639091751465, (44, 25851): 571.7068681270637, (44, 25874): 543.1160686246292, (44, 25898): 554.7560594177843, (44, 25946): 561.6276221874692, (44, 26047): 555.5686290180913, (44, 26066): 359.9672062976961, (44, 26197): 461.45777829260805, (44, 26212): 765.5848040194095, (44, 26253): 786.529985039024, (44, 26254): 776.8447123105353, (44, 26257): 774.991816074503, (44, 26258): 783.897299813985, (44, 26260): 778.9038609738333, (44, 26266): 774.5690361537225, (44, 26267): 770.5038374427472, (44, 26271): 771.8166022646221, (44, 26304): 692.7163645553069, (44, 26305): 689.3263792416826, (44, 26363): 603.2121710597933, (44, 26441): 1261.076871304647, (44, 26442): 1258.774518789237, (44, 26450): 1247.9771970410445, (44, 26459): 1247.5025983000814, (44, 26462): 1249.1847866398182, (44, 26467): 1280.9142679285096, (44, 26471): 1271.8265669169973, (44, 26472): 1270.8291628123297, (44, 26473): 1270.4113160724473, (44, 26476): 1264.8253740881205, (44, 26485): 1252.7012416156876, (44, 26493): 1252.8463084836537, (44, 26524): 1254.1235599419954, (44, 26525): 1252.7684405727655, (44, 26556): 1267.5530640451504, (44, 26560): 1266.8279011785307, (44, 26561): 1260.0492018545872, (44, 26564): 1264.5400558226136, (44, 26569): 1258.2693883382487, (44, 26570): 1255.4155601562395, (44, 26573): 1257.0008474476263, (44, 26581): 1256.624311583792, (44, 26583): 1254.3325919782544, (44, 26593): 1256.5482547193922, (44, 26837): 1282.9360914323179, (44, 26844): 1290.243947239583, (44, 26863): 1274.050531740664, (44, 26893): 1294.962267356655, (44, 26902): 1304.8716067770133, (44, 26905): 1295.088188975371, (44, 26912): 1302.7438668586635, (44, 26921): 1284.0839123283872, (44, 26922): 1263.8868161476673, (44, 27212): 1342.3309176343637, (44, 27218): 1334.0524043777855, (44, 27239): 1356.2913703683428, (44, 27257): 1348.7718616470672, (44, 27274): 1359.0384909915126, (44, 27279): 1357.2511650098115, (44, 27282): 1348.9752554517893, (44, 27283): 1352.6690520957854, (44, 27285): 1362.6550761130256, (44, 27286): 1354.6928389205748, (44, 27290): 1341.8650074531522, (44, 27295): 1337.0941869751107, (44, 27300): 1360.552349675329, (44, 27344): 1337.4183082394434, (44, 27366): 1346.582821015942, (44, 27383): 1362.9244850689593, (44, 27398): 1373.5474344322665, (44, 27406): 1365.4765592203755, (44, 27407): 1368.0967879554685, (44, 27426): 1358.7850629278346, (44, 27432): 1322.5102994902093, (44, 27460): 1345.4478070717282, (44, 27523): 1346.328342696143, (44, 27545): 1496.5289182241268, (44, 27602): 1683.2695023788724, (44, 27606): 1686.8962134569824, (44, 27646): 1487.6457136961844, (44, 27667): 1525.159561022865, (44, 27672): 1527.2337587997338, (44, 27674): 1520.7728738501864, (44, 27688): 1526.5577476046635, (44, 27692): 1533.599260422961, (44, 27693): 1527.9617947525019, (44, 27705): 1527.546559894983, (44, 27712): 1530.2178933924665, (44, 27786): 1695.7903939411642, (44, 27790): 1675.9782973358797, (44, 27791): 1674.3974289464888, (44, 27795): 1685.125471449996, (44, 27801): 1670.2337754167697, (44, 27813): 1701.4325617963493, (44, 27816): 1694.8400835370112, (44, 27823): 1669.682561526704, (44, 27830): 1686.842407136547, (44, 27884): 1423.8247893899852, (44, 27885): 1471.7010165040635, (44, 27896): 1442.8209597323712, (44, 27919): 1440.9497482183613, (44, 27922): 1446.7380812605315, (44, 27930): 1431.247493867727, (44, 27934): 1432.9796382376715, (44, 27935): 1434.2181369264358, (44, 27948): 1659.1514590051963, (44, 27951): 1671.0529995015424, (44, 28061): 1472.0079220730113, (44, 28290): 1868.5198269676453, (44, 28292): 1875.7911104973725, (44, 28293): 1869.869025822103, (44, 28295): 1865.9289222856432, (44, 28296): 1867.8239064471995, (44, 28297): 1864.598690657505, (44, 28302): 1861.246426674692, (44, 28310): 1962.6318798403654, (44, 28313): 1967.7177600424875, (44, 28372): 1970.876627533257, (44, 28398): 1971.3607029226014, (44, 28399): 1968.6223178024975, (44, 28400): 1972.7945132906564, (44, 28401): 1962.1040906569453, (44, 28445): 1963.2257233903624, (44, 28475): 1955.1728587259624, (44, 28885): 218.1197906946613, (44, 28886): 216.74877055354182, (44, 28915): 225.88140681925742, (44, 28916): 221.29577241464082, (44, 28917): 221.26233029968654, (44, 28921): 222.380111110459, (44, 28931): 223.1395942860655, (44, 28945): 233.86320722392472, (44, 28982): 228.03804661029105, (44, 29219): 288.3184090956889, (44, 29228): 275.52872820778583, (44, 29246): 385.6302607285075, (44, 29248): 393.2850147305395, (44, 29282): 372.1613983307537, (44, 29290): 386.4826726684166, (44, 29291): 384.8299747731637, (44, 29292): 387.56974773918006, (44, 29293): 379.5149586765389, (44, 29294): 389.4924313894399, (44, 29298): 382.35922059979094, (44, 29299): 383.96803864068295, (44, 29304): 371.4366387351697, (44, 29317): 349.30580463992794, (44, 29323): 347.3307662958224, (44, 29330): 358.37479616223334, (44, 29331): 361.9575595821263, (44, 29344): 309.3651087140781, (44, 29445): 266.05099272909564, (44, 29724): 2515.9236710250184, (44, 29738): 2519.184420049291, (44, 29745): 2509.1002857032167, (44, 29748): 2508.0787837832877, (44, 29750): 2512.185703436431, (44, 29759): 2503.964130742137, (44, 29772): 2515.969420736177, (44, 29781): 2513.265039547076, (44, 29784): 2512.4534991085898, (44, 29790): 2515.3680955741593, (44, 29811): 2507.2465568534444, (44, 29817): 2521.8643093035557, (44, 29818): 2519.181202326631, (44, 29929): 2509.7652262341508, (44, 30039): 2560.1933060298575, (44, 30066): 2537.2822456509634, (44, 30116): 2420.3176232668957, (44, 30238): 2247.364714329173, (44, 30248): 2340.5691365583816, (44, 30260): 2343.2050090762973, (44, 30545): 149.15629883378875, (44, 30733): 56.29183024405562, (44, 30756): 139.73858789937688, (44, 30921): 82.28892171196436, (44, 31079): 539.6999583757275, (44, 31149): 526.6354842733509, (44, 31154): 531.0116888076595, (44, 31160): 527.0793916393771, (44, 31163): 533.1048710550141, (44, 31189): 582.0943354985216, (44, 31215): 582.6218063225081, (44, 31259): 608.669552443734, (44, 31262): 612.796391760738, (44, 31430): 552.4509273982095, (44, 31568): 731.7399802623445, (44, 31751): 578.1326699281591, (45, 109): 2433.187803350405, (45, 872): 1186.1804112128389, (45, 873): 1182.729647344865, (45, 877): 1179.9048587010145, (45, 879): 1178.991707915495, (45, 884): 1173.306109593279, (45, 889): 1173.0586445906663, (45, 891): 1175.571908518781, (45, 892): 1177.1810760578398, (45, 894): 1179.3017576669715, (45, 896): 1189.4471624828966, (45, 903): 1175.077518519671, (45, 909): 1194.4719080495133, (45, 910): 1196.8852915376342, (45, 912): 1198.2869710779419, (45, 913): 1198.4607322806473, (45, 916): 1204.0800448287816, (45, 926): 1200.7656135420755, (45, 927): 1202.7691369207048, (45, 948): 1177.5133384645626, (45, 961): 1191.9708046513215, (45, 962): 1194.2383392142988, (45, 963): 1195.9323943685501, (45, 967): 1175.286645636375, (45, 974): 1167.5491385093158, (45, 998): 1170.5354125388594, (45, 1014): 1158.6496805007894, (45, 1086): 1305.469919296217, (45, 1087): 1319.5566439361485, (45, 1089): 1315.1338783100327, (45, 1090): 1312.7485859419733, (45, 1092): 1308.4392954631714, (45, 1097): 1309.0170287506337, (45, 1107): 1315.0375000193826, (45, 1387): 2050.7355368363947, (45, 1554): 2111.3287093519466, (45, 1827): 979.0537746673192, (45, 1828): 980.9825758826279, (45, 1829): 979.3573629753384, (45, 1830): 969.822436143987, (45, 1831): 971.4344952644328, (45, 1832): 972.5280664614188, (45, 1833): 974.1850138307666, (45, 1836): 976.2309935685208, (45, 1841): 972.8787913543443, (45, 1843): 973.2499408377483, (45, 1844): 971.4233233653596, (45, 1845): 970.4100810511503, (45, 1847): 976.801727448896, (45, 1848): 975.6804369608761, (45, 1849): 968.8693750378935, (45, 1850): 969.8853656705465, (45, 1851): 970.3812134750048, (45, 1852): 966.4576151954267, (45, 1854): 968.974367241121, (45, 1856): 971.8585853973497, (45, 1857): 973.6506220938985, (45, 1858): 972.0390179243892, (45, 1861): 976.095858976968, (45, 1866): 968.5959068644099, (45, 1867): 976.112790834099, (45, 1868): 979.5682510633798, (45, 1870): 966.4904350245603, (45, 1871): 979.432188411595, (45, 1875): 971.6306561482321, (45, 1880): 974.6672436364271, (45, 1882): 968.870444136377, (45, 1883): 974.2481033062331, (45, 1889): 980.6367826817543, (45, 1893): 985.631342209226, (45, 1894): 987.1889944897915, (45, 1899): 983.6950230053278, (45, 1900): 984.6660656461437, (45, 1902): 984.8492324743235, (45, 1905): 981.7450274691654, (45, 1907): 979.100835538559, (45, 1910): 983.6498412956495, (45, 1917): 993.2008649277276, (45, 1920): 982.4577356741768, (45, 1935): 989.1057390009488, (45, 1937): 987.3577729937473, (45, 1946): 993.4564672308969, (45, 1949): 994.9768399125173, (45, 1950): 986.8348919916228, (45, 1951): 988.6263625538015, (45, 1952): 978.1117992218788, (45, 1953): 987.0870492341747, (45, 1954): 980.6834478379445, (45, 1958): 990.9335580725719, (45, 1960): 987.7480675546642, (45, 1968): 986.5181452191703, (45, 1969): 996.5174382780003, (45, 1974): 993.2082869464938, (45, 1975): 990.6953055306385, (45, 1979): 996.2374261940619, (45, 1980): 988.7714283732383, (45, 1981): 993.3255330531774, (45, 1985): 995.2777951008554, (45, 1994): 970.1215074227538, (45, 2011): 966.3271217314278, (45, 2019): 953.2103362827027, (45, 2020): 954.8645622451704, (45, 2029): 953.906787637095, (45, 2030): 956.1331670224032, (45, 2032): 949.9877252802216, (45, 2033): 954.1607971447161, (45, 2034): 950.4673596151947, (45, 2036): 935.565254686948, (45, 2037): 939.9518214230553, (45, 2038): 957.2107992108007, (45, 2042): 950.0067475304029, (45, 2050): 959.872334035772, (45, 2051): 955.9962064026082, (45, 2053): 957.5465013304007, (45, 2054): 956.7512413142198, (45, 2066): 957.6766435161169, (45, 2067): 959.7116209254269, (45, 2071): 973.4221075393451, (45, 2072): 975.2259057582888, (45, 2073): 988.4690475315081, (45, 2074): 986.1138601660085, (45, 2080): 981.7429278786808, (45, 2082): 975.3237001235386, (45, 2083): 976.5175604743102, (45, 2089): 980.3180244593668, (45, 2090): 982.0979771358622, (45, 2092): 984.8705119594302, (45, 2098): 986.0822703222129, (45, 2099): 983.1812046298928, (45, 2101): 982.7428417720515, (45, 2102): 984.7392925307822, (45, 2103): 982.6805304534638, (45, 2104): 979.9308536161125, (45, 2106): 974.6942732597109, (45, 2112): 979.7757351150317, (45, 2113): 982.9067423042675, (45, 2114): 977.4177866571896, (45, 2117): 971.9415904619569, (45, 2123): 1107.8927153414022, (45, 2124): 1108.4185927644967, (45, 2134): 1097.7412237945007, (45, 2138): 1102.9345183329362, (45, 2141): 1100.7461238798303, (45, 2148): 1065.7897445023152, (45, 2150): 1097.8424938563676, (45, 2151): 1095.7371348644576, (45, 2152): 1095.152470712425, (45, 2153): 1069.357292649072, (45, 2154): 1069.6321243734496, (45, 2155): 1063.3991202142395, (45, 2156): 1067.3617815236264, (45, 2157): 1045.8767696920506, (45, 2160): 1086.450046380187, (45, 2161): 1091.537355379561, (45, 2162): 1055.9056097200692, (45, 2163): 1056.439857083576, (45, 2164): 1054.228486276572, (45, 2168): 1079.758183333866, (45, 2172): 1063.8528398598637, (45, 2174): 1091.1936168777077, (45, 2178): 1059.4355256061247, (45, 2179): 1057.7889586196968, (45, 2183): 1098.7642939252607, (45, 2185): 1096.5884189943117, (45, 2186): 1097.3477498373582, (45, 2190): 1090.461200952687, (45, 2192): 1091.057556913635, (45, 2193): 1100.1456570917842, (45, 2194): 1100.7455052519554, (45, 2195): 1096.1006103517482, (45, 2197): 1088.6096536363602, (45, 2205): 1082.7812418800113, (45, 2207): 1076.754844855052, (45, 2208): 1079.1739903824082, (45, 2212): 1110.3626465626464, (45, 2214): 1041.8227157755698, (45, 2225): 1027.5682442220418, (45, 2231): 1128.20695064367, (45, 2278): 993.094521009699, (45, 2284): 984.6337821899856, (45, 2285): 981.6447654367983, (45, 2291): 962.88614123355, (45, 2292): 987.4490837694472, (45, 2307): 984.5661697368545, (45, 2313): 955.4081265267762, (45, 2317): 998.2059409100683, (45, 2319): 984.666246844133, (45, 2321): 980.1168133492225, (45, 2323): 987.1671838992149, (45, 2326): 998.6347871145679, (45, 2327): 999.0270147896495, (45, 2329): 998.5796667147129, (45, 2330): 996.4269929965417, (45, 2332): 992.4572324473974, (45, 2344): 1003.5991866506818, (45, 2346): 998.731721944313, (45, 2361): 1039.7366198476193, (45, 2368): 1012.2361806765769, (45, 2374): 1008.1294607686991, (45, 2375): 1010.4962136136685, (45, 2377): 1015.3398561793554, (45, 2378): 1008.1808501940667, (45, 2379): 1003.1811683105595, (45, 2380): 1006.5853754358997, (45, 2383): 1017.9807876836817, (45, 2385): 1019.4982979855718, (45, 2395): 1023.8728831638475, (45, 2397): 1001.0933321778662, (45, 2398): 1016.376627984908, (45, 2399): 1018.0480698914985, (45, 2400): 1018.2873356482734, (45, 2402): 1003.4857076650965, (45, 2403): 1002.7645055300175, (45, 2404): 1004.6123261861053, (45, 2405): 1004.5331235312324, (45, 2407): 1007.537471734935, (45, 2408): 1004.6001982095007, (45, 2409): 1005.3246151214615, (45, 2411): 994.5247782722446, (45, 2412): 997.8049382465764, (45, 2413): 996.0860229813311, (45, 2414): 995.9226508513124, (45, 2422): 991.8671747379078, (45, 2424): 999.4119000561248, (45, 2426): 1000.9366261061567, (45, 2433): 998.9844891015988, (45, 2436): 993.9309122215817, (45, 2437): 999.615931829365, (45, 2440): 999.8001966426289, (45, 2445): 939.955307508532, (45, 2447): 946.1429118557223, (45, 2454): 944.9156436516103, (45, 2455): 948.8375604626839, (45, 2460): 947.6494709208675, (45, 2461): 946.8716309410432, (45, 2471): 918.1387005367387, (45, 2492): 770.1459502075573, (45, 2511): 800.6095657957108, (45, 2523): 784.3547718430516, (45, 2525): 776.7077058736686, (45, 2535): 857.292504710974, (45, 2537): 855.6325559015098, (45, 2538): 860.72697888628, (45, 2539): 841.4307294490916, (45, 2540): 857.5670981530016, (45, 2542): 851.9867811411185, (45, 2559): 894.770824741157, (45, 2575): 870.5032862581056, (45, 2599): 927.3730993707284, (45, 2600): 911.9843127845345, (45, 2607): 935.725747492111, (45, 2627): 729.0502132681454, (45, 2647): 713.6516640555486, (45, 2674): 735.7959488989001, (45, 2681): 725.8701169831123, (45, 2683): 729.4638184400404, (45, 2686): 735.5933798081213, (45, 2689): 721.4047711679331, (45, 2690): 718.936510597914, (45, 2713): 646.2378539386686, (45, 2714): 636.3928195237904, (45, 2715): 637.1591895430187, (45, 2739): 639.4289634656111, (45, 2740): 662.9190694108539, (45, 2741): 665.2323487029578, (45, 2749): 627.8707915012508, (45, 2750): 631.6446279329575, (45, 2752): 633.7823074167619, (45, 2755): 632.1254137733981, (45, 2758): 628.9716885897484, (45, 2759): 630.568472832498, (45, 2769): 633.7696731456557, (45, 2771): 656.6787727943416, (45, 2779): 630.9607697011419, (45, 2784): 613.6712765361724, (45, 2800): 589.1251498424378, (45, 2802): 647.9256299386523, (45, 2803): 650.9621135222577, (45, 2804): 651.888293125444, (45, 2805): 638.5990820188642, (45, 2807): 641.8475911021136, (45, 2809): 634.3160926258644, (45, 2812): 639.4164256125634, (45, 2814): 612.4562667856651, (45, 2817): 583.389489862969, (45, 2819): 649.9600183100919, (45, 2823): 611.3617333105464, (45, 2832): 634.6481950516031, (45, 2836): 632.7257775862531, (45, 2839): 645.1706999283804, (45, 2841): 598.2835562172576, (45, 2843): 603.3486678184197, (45, 2846): 619.8626719446611, (45, 2849): 629.4490363073475, (45, 2852): 631.070862884831, (45, 2853): 628.5063194169276, (45, 2876): 613.4997577038018, (45, 2877): 613.11392478241, (45, 2885): 582.8864570469126, (45, 2918): 671.2154460416381, (45, 2921): 667.9568552987309, (45, 2925): 694.175241174528, (45, 2926): 709.1990603187253, (45, 2930): 658.5050562352309, (45, 2931): 685.3239029624242, (45, 2938): 665.5075936511885, (45, 2940): 694.3586250531372, (45, 2947): 699.379884245352, (45, 2949): 671.4230602276397, (45, 2950): 666.0510283516074, (45, 2952): 665.6179303682417, (45, 2958): 667.8823666945294, (45, 2959): 674.6505148114404, (45, 2960): 673.0859382861348, (45, 2961): 670.210339778086, (45, 2963): 664.4047403244508, (45, 2968): 661.2266537629891, (45, 2976): 667.7513931003293, (45, 2981): 623.1561976753998, (45, 2982): 616.3710237133369, (45, 2984): 614.6450378601855, (45, 3003): 606.9437050883155, (45, 3046): 681.5387876355445, (45, 3050): 646.5742358133934, (45, 3051): 649.2436659991392, (45, 3053): 646.0983241850654, (45, 3069): 637.4114225815763, (45, 3071): 661.288716614275, (45, 3080): 571.8459162577599, (45, 3199): 565.7570710850458, (45, 3200): 560.7781807832228, (45, 3205): 568.452412586682, (45, 3209): 560.2862521823033, (45, 3215): 564.4683408554693, (45, 3217): 562.8946535465387, (45, 3249): 568.4652262913222, (45, 3263): 584.406908332837, (45, 3289): 582.9080227102958, (45, 3301): 573.8118629024099, (45, 3302): 576.671869384756, (45, 3307): 576.886858475698, (45, 3310): 574.5886753878332, (45, 3391): 394.98303617363933, (45, 3509): 1164.133888727826, (45, 3510): 1167.92052585242, (45, 3511): 1167.580747588382, (45, 3512): 1171.833757985338, (45, 3514): 1172.7868929351755, (45, 3519): 1144.663863143068, (45, 3536): 1161.3592636513408, (45, 3545): 1157.7473032495936, (45, 3548): 1166.407426533973, (45, 3572): 1156.5355057659797, (45, 3581): 1153.8460833698416, (45, 3583): 1165.38121160555, (45, 3601): 1134.1764339983097, (45, 3656): 1132.3883110292923, (45, 3669): 1123.5443225802003, (45, 3670): 1119.3014153784807, (45, 3695): 1146.3353031250954, (45, 3696): 1143.8076599658368, (45, 3782): 1206.0605084817744, (45, 3792): 1203.4780989548335, (45, 3989): 2905.698976411237, (45, 4008): 2925.2158427293502, (45, 4031): 2916.2342522501785, (45, 4045): 2916.655087133502, (45, 4144): 2924.9105880442403, (45, 4145): 2913.0222083469043, (45, 4164): 2919.1900038400095, (45, 4168): 2916.712638197555, (45, 4173): 2917.2699491915873, (45, 4181): 2905.2994541042503, (45, 4228): 2885.8540607466975, (45, 4248): 2891.9480132534077, (45, 4254): 2817.2142531105737, (45, 4260): 2814.24021775971, (45, 4262): 2823.3513271355055, (45, 4273): 2819.67893309132, (45, 4319): 2771.345500233956, (45, 4326): 2768.4685974148856, (45, 4328): 2768.4390292685284, (45, 4334): 2774.973995695747, (45, 4335): 2774.0013469196037, (45, 4372): 2874.9314578993767, (45, 4413): 2954.559894013331, (45, 4434): 2871.3383511353454, (45, 4447): 2880.764921402488, (45, 4452): 2872.580821052231, (45, 4463): 2716.4723514240745, (45, 4465): 2721.6684005649054, (45, 4619): 2965.3859113843273, (45, 4645): 2982.3132155570843, (45, 4657): 2979.7574418470826, (45, 4666): 2973.2197947294358, (45, 4676): 2985.1846470900377, (45, 4678): 2987.79333622163, (45, 4689): 2979.7850648430667, (45, 4704): 3039.198877959909, (45, 4726): 3181.5834000826258, (45, 4727): 3178.967469519469, (45, 4730): 3173.91479762129, (45, 4731): 3175.218803425117, (45, 4734): 3178.896617609771, (45, 4735): 3176.2952139090385, (45, 4736): 3177.44238415096, (45, 4737): 3172.8960091374397, (45, 4738): 3173.39805531821, (45, 4756): 3175.9501414039105, (45, 4760): 3163.39524111663, (45, 4761): 3165.109524363568, (45, 4762): 3159.6682154880577, (45, 4765): 3164.616916262879, (45, 4773): 3186.8586645410273, (45, 4774): 3184.2493637775087, (45, 4790): 3185.161612051359, (45, 4795): 3182.944727177259, (45, 4799): 3185.232552912018, (45, 4801): 3190.319518944913, (45, 4804): 3184.1726562724616, (45, 4805): 3182.345033914803, (45, 4806): 3182.8451711724983, (45, 4815): 3180.0924058787555, (45, 4816): 3186.7674523859096, (45, 4817): 3187.731996713689, (45, 4826): 3183.9368829172204, (45, 4830): 3180.0848930375037, (45, 4839): 3171.017277153749, (45, 4840): 3173.2306883373353, (45, 4841): 3167.608090643843, (45, 4846): 3165.840833575614, (45, 4848): 3164.994144398009, (45, 4850): 3167.3313052062067, (45, 4871): 3137.9982498399004, (45, 4883): 3160.7952589664997, (45, 4900): 3149.4024586653245, (45, 4901): 3145.9519508109533, (45, 4917): 2960.1257191632994, (45, 4931): 2940.645833601625, (45, 4944): 2962.5323837374503, (45, 4956): 2944.0209653653387, (45, 4958): 2943.062289116826, (45, 4959): 2939.092092005662, (45, 4961): 2948.125615734298, (45, 4966): 2939.032482403632, (45, 5207): 2917.406260234268, (45, 5272): 2546.428729849925, (45, 5283): 2553.73993968054, (45, 5287): 2565.4001242601717, (45, 5289): 2568.5944286456593, (45, 5293): 2547.695274656996, (45, 5295): 2568.1675104122014, (45, 5296): 2568.0469758043687, (45, 5298): 2567.813956896956, (45, 5303): 2573.8447854007086, (45, 5305): 2542.263408403433, (45, 5306): 2536.620450488972, (45, 5307): 2538.4809799502746, (45, 5308): 2545.6223860216987, (45, 5313): 2545.2840385721693, (45, 5314): 2549.876163438933, (45, 5317): 2545.67622101847, (45, 5319): 2566.8229246612136, (45, 5324): 2562.6979192711556, (45, 5326): 2560.035092095627, (45, 5348): 2534.939070530006, (45, 5351): 2540.315763237053, (45, 5399): 2572.680548650401, (45, 5413): 2549.5010321775967, (45, 5422): 2576.633667153541, (45, 5445): 2560.003812548118, (45, 5448): 2553.0739206694907, (45, 5456): 2551.4398257781054, (45, 5467): 2557.869682877707, (45, 5624): 2481.3893383737613, (45, 5671): 2707.0167609414866, (45, 5672): 2697.4466393547414, (45, 5797): 2820.4692593243813, (45, 5871): 2668.389914154541, (45, 5976): 2587.4648936265253, (45, 6118): 538.508272337371, (45, 6248): 396.3828351127407, (45, 6345): 2043.837192938734, (45, 6352): 2020.4594939720146, (45, 6354): 2050.2532080567134, (45, 6359): 2053.6275002923057, (45, 6376): 2021.148217799216, (45, 6378): 2047.3381478599226, (45, 6381): 2050.8538895381707, (45, 6383): 2039.376474991097, (45, 6396): 2043.3849282404585, (45, 6399): 2042.637317311917, (45, 6408): 2022.5550956408651, (45, 6409): 2036.9011266513432, (45, 6419): 2004.5941802083946, (45, 6422): 2028.2541333622214, (45, 6423): 2026.5567748585863, (45, 6424): 2051.7322514191073, (45, 6439): 2048.353686692886, (45, 6464): 2042.9627458067403, (45, 6465): 2039.4502753165984, (45, 6469): 2039.8943747323415, (45, 6470): 2037.899322423297, (45, 6472): 2061.066376557216, (45, 6480): 2061.797638003888, (45, 6486): 2081.8900320315556, (45, 6497): 2075.4250291554495, (45, 6503): 2051.718011811387, (45, 6508): 2049.4103313390083, (45, 6509): 2055.7143632326547, (45, 6521): 2067.3151882003244, (45, 6544): 2069.4539845078316, (45, 6552): 2038.4766751075886, (45, 6553): 2035.2462149805278, (45, 6554): 2031.9098327434674, (45, 6578): 2043.3331840315957, (45, 6582): 2044.7995233887093, (45, 6601): 2045.649864773529, (45, 6609): 2068.5515053560175, (45, 6610): 2070.3210152142847, (45, 6611): 2068.9066842030516, (45, 6614): 2065.909588996916, (45, 6615): 2067.253616310285, (45, 6616): 2073.495250231528, (45, 6617): 2070.986278199582, (45, 6618): 2078.756436602898, (45, 6619): 2063.856945581334, (45, 6620): 2074.8781676607623, (45, 6621): 2072.2580819378227, (45, 6622): 2072.023870153129, (45, 6623): 2066.9995333132715, (45, 6624): 2065.7792715215687, (45, 6625): 2064.5360333277936, (45, 6626): 2063.1362422743655, (45, 6627): 2064.0841149109965, (45, 6628): 2075.624423271253, (45, 6629): 2068.188246985807, (45, 6630): 2059.981614725364, (45, 6632): 2067.1639175300184, (45, 6634): 2057.6742924841233, (45, 6635): 2070.5080465885712, (45, 6636): 2074.1104232837934, (45, 6637): 2064.36335816301, (45, 6638): 2061.558528607258, (45, 6639): 2065.125984735264, (45, 6640): 2061.394950190763, (45, 6641): 2073.2195165571325, (45, 6642): 2062.4870211695174, (45, 6643): 2061.900523777288, (45, 6645): 2064.8461126996363, (45, 6646): 2076.681492680004, (45, 6647): 2062.8809030909006, (45, 6653): 2066.7276684279523, (45, 6655): 2064.7455274418576, (45, 6658): 2057.96332219006, (45, 6662): 2063.250121710271, (45, 6819): 1917.4503152204986, (45, 6996): 1996.1541322917824, (45, 7059): 2033.1871261385254, (45, 7187): 2029.107144602002, (45, 7304): 1915.3850221137734, (45, 7528): 2017.4729391468193, (45, 7720): 2218.608647060799, (45, 7793): 2222.8403045068267, (45, 7807): 2222.99410214777, (45, 7808): 2223.8038937087867, (45, 7831): 2098.7398317705824, (45, 7850): 2128.380466157856, (45, 7852): 2118.2162935793085, (45, 8012): 2195.989858293905, (45, 8125): 2289.1006067100175, (45, 8208): 2289.06157833177, (45, 8392): 2149.031244351111, (45, 8651): 1740.2560602211195, (45, 9088): 1877.2705957848236, (45, 9443): 1753.5292985660085, (45, 9444): 1760.1524841187936, (45, 9828): 1656.0335764484794, (45, 9868): 1600.9004665931013, (45, 10180): 2296.900617159749, (45, 10256): 2396.51754498288, (45, 10276): 2343.276087855227, (45, 10378): 2332.0168997361325, (45, 10676): 2302.154574738311, (45, 10714): 2250.0397124821275, (45, 10730): 2232.888777941981, (45, 10862): 2419.3704785798877, (45, 10881): 2434.800887470879, (45, 10883): 2433.3552458939475, (45, 10885): 2415.9850037295814, (45, 10891): 2431.142111910038, (45, 10909): 2429.1566385798956, (45, 10911): 2430.6724941569673, (45, 10913): 2427.3203904231464, (45, 10915): 2426.825226193877, (45, 10919): 2428.6918215612445, (45, 11037): 2333.415043646075, (45, 11039): 2291.0285442032646, (45, 11516): 3038.260830421611, (45, 11856): 2777.2654819462305, (45, 11857): 2777.494994526466, (45, 11861): 2777.5894821771253, (45, 11881): 2768.967103728997, (45, 11902): 2752.7968547999353, (45, 11911): 2746.280787280625, (45, 11914): 2750.094749640642, (45, 11922): 2763.355011221799, (45, 11924): 2766.2439008095107, (45, 11926): 2761.373674453129, (45, 11950): 2766.6056692077873, (45, 11963): 2782.3932284949933, (45, 11983): 2765.3719967532784, (45, 11985): 2790.6473755792936, (45, 12009): 2781.9994599670317, (45, 12010): 2772.2135878508807, (45, 12018): 2773.291328995114, (45, 12020): 2777.130383419217, (45, 12021): 2778.357556568836, (45, 12024): 2789.005956930388, (45, 12025): 2786.555131040282, (45, 12027): 2783.7495371585046, (45, 12031): 2770.3831490466255, (45, 12032): 2774.9762542618964, (45, 12035): 2779.9887801216178, (45, 12041): 2795.2584275701834, (45, 12045): 2642.2045482771823, (45, 12145): 2704.007119941132, (45, 12275): 2898.9611548911403, (45, 12294): 2863.3870619282966, (45, 12358): 2944.287016710686, (45, 12463): 2971.0772355140407, (45, 12465): 2969.6371235448332, (45, 12482): 2990.9304310955285, (45, 12503): 2987.2683881314083, (45, 12506): 2991.5186132812555, (45, 12549): 2989.713823464625, (45, 12559): 2984.994317936545, (45, 12569): 2985.857746777062, (45, 12572): 2989.2060014790663, (45, 12574): 2983.0252235287294, (45, 12576): 2994.305258947883, (45, 12591): 2997.7840585395197, (45, 12608): 3026.919461777602, (45, 12696): 2988.016502974997, (45, 12710): 3018.015581343208, (45, 12728): 3000.09758421133, (45, 12766): 2332.096064306564, (45, 12771): 2318.718680188075, (45, 12790): 2314.361473672718, (45, 12795): 2302.4512826995037, (45, 12797): 2275.8856625033354, (45, 12798): 2281.3697461879224, (45, 12811): 2308.9013674514754, (45, 12830): 2296.773034844586, (45, 12848): 2307.4429029557436, (45, 12850): 2313.297862899157, (45, 12852): 2297.2053991826897, (45, 12854): 2292.9223161905984, (45, 12859): 2313.2444307188084, (45, 12861): 2287.410479812688, (45, 12865): 2311.602058258615, (45, 12866): 2311.108426261223, (45, 12867): 2318.1676442704115, (45, 12874): 2314.5025205407555, (45, 12875): 2318.486268914499, (45, 12881): 2303.197016257651, (45, 12883): 2308.7063087780975, (45, 12885): 2320.918395526738, (45, 12888): 2307.373685857905, (45, 12889): 2307.293855733631, (45, 12892): 2314.7662887868923, (45, 12893): 2306.392173489543, (45, 12896): 2310.148906153292, (45, 12906): 2309.58452360518, (45, 13018): 2240.522719524625, (45, 13071): 2234.4397176020066, (45, 13131): 2225.47094825055, (45, 13146): 2259.9985223414888, (45, 13159): 2185.7667629408706, (45, 13193): 2221.803458343123, (45, 13198): 2182.246727894219, (45, 13292): 2243.8569479658117, (45, 13296): 2272.5623842815016, (45, 13406): 2131.7504713241196, (45, 13407): 2128.59502212061, (45, 13417): 2113.121143553943, (45, 13418): 2116.8151839331695, (45, 13438): 2148.446837241066, (45, 13442): 2156.786585136852, (45, 13443): 2151.935996716029, (45, 13764): 1685.5891330448014, (45, 13766): 1691.626926676522, (45, 13771): 1682.005537683148, (45, 13783): 1686.890087086738, (45, 13784): 1699.8288428230585, (45, 13792): 1664.8025734750875, (45, 13824): 1681.9929546693563, (45, 14017): 1740.1568381421278, (45, 14870): 2405.084973575724, (45, 14997): 2007.6279282190435, (45, 15000): 2011.1925622734336, (45, 15003): 2018.039090368729, (45, 15006): 2013.420106460213, (45, 15007): 2017.6142279619744, (45, 15056): 2026.06065819148, (45, 15063): 2024.3674734041665, (45, 15069): 2026.5127810276304, (45, 15076): 2020.334364493966, (45, 15086): 2004.3267810262903, (45, 15087): 2004.3004862736834, (45, 15111): 1989.662050177027, (45, 15116): 1998.3709222999714, (45, 15722): 1893.4813114521767, (45, 15998): 1908.1993987262015, (45, 16073): 803.3704510562825, (45, 16939): 900.6345190674059, (45, 16940): 904.0048833572197, (45, 16951): 887.7553097200683, (45, 16963): 890.4949967413627, (45, 16965): 891.8889055797933, (45, 16969): 885.0494386425789, (45, 16970): 893.4067305403737, (45, 16971): 892.6373803028903, (45, 16973): 888.1301084421507, (45, 16974): 888.1631894617507, (45, 16976): 896.306204374023, (45, 16978): 897.2923681447292, (45, 16980): 900.4352961539416, (45, 16982): 883.4703494932136, (45, 17045): 519.2216483859734, (45, 17048): 518.3541980771923, (45, 17304): 2872.476848764036, (45, 17305): 2864.0752654481616, (45, 17330): 2869.125098490789, (45, 17334): 2865.9051755694413, (45, 17343): 2873.742045359924, (45, 17345): 2860.8079529618794, (45, 17347): 2865.462991495207, (45, 17351): 2855.8689742316146, (45, 17372): 2863.2562412632833, (45, 17373): 2874.044823852192, (45, 17377): 2874.4069106945435, (45, 17382): 2866.3608766148295, (45, 17383): 2869.4740151414594, (45, 17389): 2864.333932637347, (45, 17400): 2873.317985782548, (45, 17401): 2873.922818150784, (45, 17402): 2873.328728444728, (45, 17403): 2873.74012419908, (45, 17440): 2856.060928977603, (45, 17455): 2869.1436165513946, (45, 17491): 2866.3341988657403, (45, 17507): 2872.1600512473706, (45, 17509): 2878.0564658801704, (45, 17590): 2847.3682034800145, (45, 17615): 2852.2077993702123, (45, 17642): 2854.5122255878982, (45, 17643): 2852.2670301473086, (45, 17668): 2853.1686710315, (45, 17721): 2852.410692989041, (45, 17754): 2899.8923516521554, (45, 17769): 2879.1787673662443, (45, 17776): 2851.7045629654967, (45, 17804): 2887.69745323746, (45, 17809): 2892.45794266845, (45, 17824): 2892.388430823191, (45, 17837): 2864.3674811207165, (45, 17838): 2862.1595245756534, (45, 17862): 2857.328346208978, (45, 17866): 2868.7248060855823, (45, 17872): 2855.575620150118, (45, 17873): 2846.2612177626643, (45, 17881): 2860.149243677242, (45, 17947): 1305.0987874873745, (45, 17951): 1304.573844664236, (45, 17953): 1308.0017592209283, (45, 17954): 1310.3337625873023, (45, 17959): 1298.9039000696994, (45, 17963): 1292.6268776985087, (45, 18000): 1302.3861793268036, (45, 18001): 1306.756509081794, (45, 18111): 1466.5780038071912, (45, 18148): 1507.1087941380465, (45, 18166): 1503.4204500325984, (45, 18189): 1467.7292145404842, (45, 18239): 2878.2806057447974, (45, 18240): 2877.652031581213, (45, 18245): 2878.4274619196167, (45, 18247): 2876.7812860503846, (45, 18251): 2877.7130690924755, (45, 18256): 2878.05596125566, (45, 18258): 2876.536675125901, (45, 18259): 2876.442178042746, (45, 18260): 2876.47192110691, (45, 18262): 2876.95048227618, (45, 18263): 2878.041490331808, (45, 18264): 2878.1077652243125, (45, 18266): 2876.792218286951, (45, 18267): 2876.9376554949076, (45, 18268): 2876.7948565454058, (45, 18269): 2877.0233621069506, (45, 18275): 2876.912986928621, (45, 18285): 2878.3112779617895, (45, 18308): 2875.845615833614, (45, 18313): 2873.395315510953, (45, 18314): 2872.7325785825838, (45, 18315): 2878.598247106084, (45, 18316): 2877.791670052864, (45, 18317): 2877.8501767263106, (45, 18320): 2879.018618636943, (45, 18321): 2878.703835047541, (45, 18322): 2878.952373006903, (45, 18324): 2880.2516853434313, (45, 18325): 2882.0931588316885, (45, 18326): 2881.4424357660114, (45, 18327): 2877.2607673297157, (45, 18329): 2883.778860805611, (45, 18330): 2880.4664555363775, (45, 18331): 2879.6123549054105, (45, 18332): 2878.3356957173532, (45, 18333): 2880.9582874879725, (45, 18336): 2881.074348168074, (45, 18337): 2882.1904938803564, (45, 18403): 2876.9378490019985, (45, 18432): 2829.5428432667723, (45, 18451): 2861.522831368131, (45, 18466): 2894.8430267287026, (45, 18481): 2881.109486102499, (45, 18483): 2880.568183799646, (45, 18484): 2879.9690317806867, (45, 18485): 2878.711404390922, (45, 18486): 2883.3531369758343, (45, 18487): 2881.646897116509, (45, 18489): 2881.2423383921086, (45, 18490): 2885.06018836927, (45, 18491): 2886.172150663897, (45, 18492): 2878.8205248807735, (45, 18493): 2883.600909064729, (45, 18494): 2880.3540524537557, (45, 18495): 2884.3124882922116, (45, 18496): 2882.704694205973, (45, 18497): 2881.7518848877116, (45, 18498): 2880.1013668086475, (45, 18499): 2881.62969299893, (45, 18501): 2881.4755653326956, (45, 18502): 2880.5592899017693, (45, 18503): 2879.200443815334, (45, 18504): 2882.499801676006, (45, 18506): 2883.169403396719, (45, 18507): 2882.60117076993, (45, 18508): 2881.9396589302332, (45, 18509): 2882.470307294115, (45, 18510): 2879.9779350258623, (45, 18511): 2884.995299177421, (45, 18512): 2882.8120986852723, (45, 18515): 2883.3583768138965, (45, 18516): 2885.2064671377098, (45, 18517): 2884.8187020936607, (45, 18518): 2885.546983852099, (45, 18519): 2882.4019174788305, (45, 18520): 2881.005156753632, (45, 18522): 2885.5743135196817, (45, 18523): 2886.3894842208397, (45, 18532): 2888.659596058574, (45, 18535): 2884.5473585539107, (45, 18537): 2882.258489377991, (45, 18539): 2883.043665399832, (45, 18540): 2883.634191003326, (45, 18541): 2885.0287800941555, (45, 18542): 2885.8584039634347, (45, 18543): 2881.977365396501, (45, 18546): 2884.8164561619596, (45, 18555): 2888.4600058660762, (45, 18556): 2889.5221418411106, (45, 18565): 2889.1826912354, (45, 18567): 2891.3966134849275, (45, 18568): 2888.918357439394, (45, 18577): 2902.9236255321534, (45, 18583): 2898.961889136807, (45, 18605): 2899.970542277326, (45, 18608): 2894.9421092417783, (45, 18616): 2913.171365745794, (45, 18618): 2925.4397255018084, (45, 18625): 2917.314774340862, (45, 18645): 2905.6584954833274, (45, 18646): 2909.64997530131, (45, 18653): 2904.397932181428, (45, 18654): 2913.5838900894105, (45, 18655): 2908.423434421085, (45, 18666): 2937.6543870768237, (45, 18837): 2834.8152936897877, (45, 18974): 2847.8082522913023, (45, 18999): 2849.915872205212, (45, 19000): 2853.1065372772505, (45, 19174): 2665.0984877866963, (45, 19342): 2717.923801681856, (45, 19455): 2715.3539157262658, (45, 19555): 2543.2414020355964, (45, 19564): 2538.535483868148, (45, 19573): 2534.881288488081, (45, 19586): 2534.1544108217317, (45, 19605): 2538.853121554348, (45, 19611): 2541.8533445139483, (45, 19614): 2544.2733996085176, (45, 19641): 2611.668838086321, (45, 19702): 2606.146614727282, (45, 19713): 2602.093975414298, (45, 19731): 2538.3758300527597, (45, 19819): 2682.5878976851977, (45, 19893): 2691.7579425389595, (45, 19899): 2735.1690752467184, (45, 19929): 2701.2671586405118, (45, 19951): 2780.9571143949306, (45, 19962): 2711.377174868368, (45, 19970): 2721.57109723787, (45, 19971): 2723.6330756658667, (45, 19972): 2718.1611998104017, (45, 19975): 2713.8179415937, (45, 19978): 2790.447878678835, (45, 19987): 2790.728271263156, (45, 19989): 2768.8620377260945, (45, 20039): 2794.222263450338, (45, 20043): 2801.861811039758, (45, 20047): 2793.5460759912216, (45, 20052): 2770.572739044377, (45, 20054): 2773.191022734553, (45, 20085): 2872.8268496711585, (45, 20104): 2879.338885272955, (45, 20132): 2840.9537820638056, (45, 20203): 2702.6207409749113, (45, 20280): 2698.425240779003, (45, 20285): 2698.122883339043, (45, 20290): 2701.3002614870875, (45, 20297): 2693.6166718495397, (45, 20309): 2807.1864399519927, (45, 20453): 2909.1947601086504, (45, 20485): 2645.7266321089346, (45, 20520): 2626.0180948814073, (45, 20526): 2623.974010219004, (45, 20698): 1457.4565023592988, (45, 20868): 1237.1760513091783, (45, 21042): 2382.5915617588744, (45, 21057): 2419.8366860342394, (45, 21066): 2404.9733377721477, (45, 21075): 2393.043396400502, (45, 21093): 2390.155425853796, (45, 21098): 2423.57417738993, (45, 21127): 2388.1895400327135, (45, 21130): 2397.559040412818, (45, 21144): 2392.0110511492067, (45, 21146): 2385.7278904056966, (45, 21147): 2390.0416589852525, (45, 21148): 2398.1126156621726, (45, 21153): 2365.0889936526064, (45, 21293): 2450.7711867034272, (45, 21426): 2398.2117242366103, (45, 21442): 2430.543172811731, (45, 21451): 2433.868484351945, (45, 21466): 2416.5370442592316, (45, 21469): 2423.4302728274397, (45, 21471): 2412.9487901755915, (45, 21473): 2419.167438613919, (45, 21475): 2414.18136882221, (45, 21482): 2426.050886462, (45, 21484): 2425.5295692590125, (45, 21488): 2421.014415894933, (45, 21494): 2416.5524933552106, (45, 21498): 2421.072205753744, (45, 21500): 2415.8252594546966, (45, 21514): 2437.543425148016, (45, 21537): 2419.843246780467, (45, 21662): 2449.5360936706834, (45, 21691): 2424.6342704014764, (45, 21757): 2362.148570671481, (45, 21777): 2325.2829085767953, (45, 21778): 2319.0910980053677, (45, 21779): 2324.788576715751, (45, 21790): 2329.8374496344563, (45, 21802): 2333.886054233515, (45, 21824): 2342.5409393299983, (45, 21874): 2329.1419272044277, (45, 21879): 2329.6021767862103, (45, 21983): 2333.1505925607244, (45, 22002): 2415.1734238102786, (45, 22132): 2321.3916813619408, (45, 22261): 1737.8054970454464, (45, 22298): 1757.1072549151884, (45, 22339): 1741.912838411309, (45, 22508): 1817.373124643221, (45, 22841): 9.616214046405608, (45, 22842): 9.623981813877393, (45, 22874): 14.908174848694392, (45, 22941): 5.436746441176111, (45, 22956): 6.646000273440032, (45, 22960): 8.58262961355792, (45, 22968): 48.89337544176624, (45, 22970): 43.75100154208265, (45, 22974): 74.28265455856155, (45, 22980): 80.17583691084357, (45, 23025): 120.84374921817252, (45, 23028): 128.67876387080298, (45, 23081): 189.4569320449081, (45, 23104): 257.82420807774935, (45, 23147): 139.98418182729353, (45, 23298): 2558.8162384506, (45, 23376): 2541.7548852692616, (45, 23381): 2542.049220485889, (45, 23529): 2578.2999377972083, (45, 23556): 2567.078169954604, (45, 23718): 2539.5966499760957, (45, 24001): 2658.1030733344514, (45, 24094): 2707.830495530866, (45, 24129): 2724.9844543352688, (45, 24174): 2696.5200587763, (45, 24235): 2739.3938231583197, (45, 24259): 2751.110772789961, (45, 24260): 2750.5978033169645, (45, 24261): 2746.224842894873, (45, 24305): 2768.7847116512885, (45, 24306): 2773.07777524681, (45, 24307): 2767.496888589337, (45, 24308): 2688.661145413311, (45, 24498): 2797.940009472935, (45, 24499): 2798.6646088490693, (45, 24500): 2795.09607951288, (45, 24668): 2754.906341654692, (45, 24711): 2827.669242587127, (45, 24756): 2846.105361123815, (45, 24788): 2848.2362173496417, (45, 24809): 2835.7133417220975, (45, 24813): 2839.0296452753682, (45, 24821): 2837.66768509654, (45, 24825): 2839.8551327479504, (45, 24832): 2833.924222061325, (45, 24833): 2836.5121444165425, (45, 24835): 2839.448013254917, (45, 24837): 2842.727064470136, (45, 24840): 2833.9557048533684, (45, 24841): 2837.059330132573, (45, 24844): 2834.6591795602594, (45, 24845): 2834.728544316524, (45, 24846): 2837.725157202627, (45, 24849): 2839.417019056883, (45, 24850): 2840.5351282831953, (45, 24863): 2800.3438557545787, (45, 24866): 2804.743304920948, (45, 24885): 2812.1690916571015, (45, 24886): 2813.8407846324503, (45, 24889): 2819.361320981762, (45, 24903): 2821.249427570029, (45, 24909): 2801.370457289853, (45, 24999): 2985.1697059651306, (45, 25019): 2974.8158104720737, (45, 25028): 2983.6043163839304, (45, 25137): 2732.5559120624894, (45, 25145): 2739.428033038368, (45, 25208): 2836.4214388377977, (45, 25233): 2827.5676211497425, (45, 25371): 2720.9453085289842, (45, 25377): 2697.4494069162747, (45, 25828): 2331.5662227038324, (45, 25851): 2266.5353461191035, (45, 25874): 2321.8534669204478, (45, 25898): 2355.353894237913, (45, 25946): 2325.3453761974597, (45, 26047): 2459.0000712985784, (45, 26066): 2543.775070029603, (45, 26197): 2481.724020832381, (45, 26212): 2193.855930415813, (45, 26253): 2180.5325126583616, (45, 26254): 2184.4210159617232, (45, 26257): 2192.864575733672, (45, 26258): 2184.302759980724, (45, 26260): 2188.4203270226826, (45, 26266): 2174.6622180752747, (45, 26267): 2180.8950297265887, (45, 26271): 2182.133703191467, (45, 26304): 2226.133917057073, (45, 26305): 2222.9885239644736, (45, 26363): 2326.2026698845675, (45, 26441): 1909.1409853182683, (45, 26442): 1907.0433785493333, (45, 26450): 1912.2030540674082, (45, 26459): 1925.145104122572, (45, 26462): 1930.0041257715725, (45, 26467): 1917.553246947984, (45, 26471): 1914.5785892087047, (45, 26472): 1913.0713155728613, (45, 26473): 1911.4006692965118, (45, 26476): 1894.790600312037, (45, 26485): 1916.7099118404697, (45, 26493): 1910.0976865972773, (45, 26524): 1933.7384009176112, (45, 26525): 1930.7810303721228, (45, 26556): 1916.884455565426, (45, 26560): 1927.8842007148494, (45, 26561): 1933.0178934137182, (45, 26564): 1915.1585602536068, (45, 26569): 1930.1909771439982, (45, 26570): 1927.2512250435063, (45, 26573): 1920.9320161409357, (45, 26581): 1916.033470721497, (45, 26583): 1920.0844917994623, (45, 26593): 1909.6793393638993, (45, 26837): 1911.5666368097293, (45, 26844): 1911.140638833845, (45, 26863): 1899.7928078895097, (45, 26893): 1893.2799810252147, (45, 26902): 1892.2434608636265, (45, 26905): 1904.4165572731488, (45, 26912): 1900.1008299880395, (45, 26921): 1897.4134826063498, (45, 26922): 1882.3437356837203, (45, 27212): 2160.2545201159874, (45, 27218): 2171.7285647565445, (45, 27239): 2157.130642890844, (45, 27257): 2153.6515498161557, (45, 27274): 2154.7769187420604, (45, 27279): 2150.5613145527786, (45, 27282): 2151.2888090725764, (45, 27283): 2159.301945529439, (45, 27285): 2151.8967072591586, (45, 27286): 2145.0698111907845, (45, 27290): 2151.231599726849, (45, 27295): 2158.0520244323316, (45, 27300): 2156.349976280822, (45, 27344): 2139.073915649344, (45, 27366): 2133.985981292555, (45, 27383): 2142.838139081041, (45, 27398): 2152.49473212201, (45, 27406): 2156.2817156133165, (45, 27407): 2159.5278055058725, (45, 27426): 2189.3328172558986, (45, 27432): 2183.2662088390266, (45, 27460): 2190.896598374202, (45, 27523): 2066.8671674246416, (45, 27545): 2132.8642480686153, (45, 27602): 2096.356090544359, (45, 27606): 2101.959766240306, (45, 27646): 2028.9877733437434, (45, 27667): 2021.9921766935759, (45, 27672): 2025.0411312991353, (45, 27674): 2024.08210759823, (45, 27688): 2036.5231142254015, (45, 27692): 2019.9821238178681, (45, 27693): 2020.2782930665933, (45, 27705): 2016.4590704953782, (45, 27712): 2013.03422095115, (45, 27786): 2235.9220801688425, (45, 27790): 2282.938618607527, (45, 27791): 2289.706671065443, (45, 27795): 2231.743067792541, (45, 27801): 2262.5145629403205, (45, 27813): 2230.5171704624263, (45, 27816): 2239.9515452586197, (45, 27823): 2264.0990825465756, (45, 27830): 2250.79043294261, (45, 27884): 2003.3826150460857, (45, 27885): 2026.1169200489278, (45, 27896): 2014.1659107470641, (45, 27919): 2016.9600167793162, (45, 27922): 2014.3793902294608, (45, 27930): 2011.3845476946792, (45, 27934): 2008.99328384137, (45, 27935): 2005.9116160651538, (45, 27948): 1916.0530951842875, (45, 27951): 1974.8443423804908, (45, 28061): 1535.018991782263, (45, 28290): 1526.0061226235189, (45, 28292): 1508.6630130820286, (45, 28293): 1521.2578467704222, (45, 28295): 1510.3954766473066, (45, 28296): 1520.171411421306, (45, 28297): 1533.998484138063, (45, 28302): 1524.2086098753487, (45, 28310): 743.293991632505, (45, 28313): 725.0656094322923, (45, 28372): 751.1509663569001, (45, 28398): 748.6165663811307, (45, 28399): 748.6832532473887, (45, 28400): 744.9551450463392, (45, 28401): 758.2115072159634, (45, 28445): 720.3055041547416, (45, 28475): 785.410310951563, (45, 28885): 2761.6368790512142, (45, 28886): 2759.1314826483417, (45, 28915): 2765.4486237510323, (45, 28916): 2761.5142231340405, (45, 28917): 2760.4324666217335, (45, 28921): 2767.1394282186398, (45, 28931): 2767.140827555565, (45, 28945): 2761.9843665618896, (45, 28982): 2762.2640258416877, (45, 29219): 2799.672566797662, (45, 29228): 2783.558954207556, (45, 29246): 2896.9079631809473, (45, 29248): 2898.744671105014, (45, 29282): 2875.9008193065224, (45, 29290): 2904.3219119528785, (45, 29291): 2900.811773619551, (45, 29292): 2904.574549514709, (45, 29293): 2895.8084580459135, (45, 29294): 2904.1857416649286, (45, 29298): 2897.346861133019, (45, 29299): 2897.4842156648265, (45, 29304): 2887.3347433641356, (45, 29317): 2865.139754514886, (45, 29323): 2863.3154597950115, (45, 29330): 2874.16329068496, (45, 29331): 2878.805811486946, (45, 29344): 2808.290412451622, (45, 29445): 2638.7722334020896, (45, 29724): 149.12850512761955, (45, 29738): 148.25279810845538, (45, 29745): 156.33414714708545, (45, 29748): 182.95116419767962, (45, 29750): 193.06581159548392, (45, 29759): 180.89410577414745, (45, 29772): 178.11770995704825, (45, 29781): 179.44384741524195, (45, 29784): 168.20215890408386, (45, 29790): 183.71718242017667, (45, 29811): 197.2447445727267, (45, 29817): 264.8753329090188, (45, 29818): 266.375118109719, (45, 29929): 139.81960076269894, (45, 30039): 56.24358930694706, (45, 30066): 17.513751554606515, (45, 30116): 151.12657314971304, (45, 30238): 344.0280477859315, (45, 30248): 213.97712810464785, (45, 30260): 209.79593632464994, (45, 30545): 2696.335855999318, (45, 30733): 2520.7656509287112, (45, 30756): 2499.94199824493, (45, 30921): 2571.412472969079, (45, 31079): 2016.600534683184, (45, 31149): 2022.8568479542164, (45, 31154): 2018.9150393809218, (45, 31160): 2022.3321150447232, (45, 31163): 2016.7093866811692, (45, 31189): 1968.500179430468, (45, 31215): 1967.2095810864205, (45, 31259): 1940.3821759462733, (45, 31262): 1936.3096302160463, (45, 31430): 2009.6190820659642, (45, 31568): 1817.7709522867062, (45, 31751): 1976.1138942350044, (47, 109): 2206.069215294127, (47, 872): 710.3453630021394, (47, 873): 705.2862054836388, (47, 877): 703.2707078102491, (47, 879): 702.1384753094275, (47, 884): 698.5801507629096, (47, 889): 697.196914288808, (47, 891): 701.3312475704889, (47, 892): 699.040563416153, (47, 894): 701.2805855952197, (47, 896): 712.6304225223271, (47, 903): 698.6246980245436, (47, 909): 720.0794292927189, (47, 910): 721.6482420093243, (47, 912): 724.1653197277261, (47, 913): 725.655154067039, (47, 916): 731.5318201178252, (47, 926): 724.7528010615808, (47, 927): 727.2505515228693, (47, 948): 703.8355281886372, (47, 961): 716.4619681347928, (47, 962): 718.4118888711631, (47, 963): 719.7950438966001, (47, 967): 698.0633206083812, (47, 974): 691.703970625294, (47, 998): 692.8450322590737, (47, 1014): 651.4845096773096, (47, 1086): 828.7505120292305, (47, 1087): 842.5788055720525, (47, 1089): 839.7369051310493, (47, 1090): 836.7693151195137, (47, 1092): 830.3612516382102, (47, 1097): 832.62607379623, (47, 1107): 835.6730910838511, (47, 1387): 1807.188252134567, (47, 1554): 1893.0275588367483, (47, 1827): 463.87369993492445, (47, 1828): 465.83174090189976, (47, 1829): 464.2842681298818, (47, 1830): 454.75721137593666, (47, 1831): 456.39572558638537, (47, 1832): 457.43344723632447, (47, 1833): 459.08250621188944, (47, 1836): 461.0639773367482, (47, 1841): 458.0245315917831, (47, 1843): 458.26824274619474, (47, 1844): 456.51216570178383, (47, 1845): 455.3625746109273, (47, 1847): 461.3020471613034, (47, 1848): 460.3166632064203, (47, 1849): 454.3152138061472, (47, 1850): 455.41317777034527, (47, 1851): 455.16129977680026, (47, 1852): 451.27742552014655, (47, 1854): 453.84737021989264, (47, 1856): 456.37028577465776, (47, 1857): 458.2910113001124, (47, 1858): 457.36899760796166, (47, 1861): 461.03940518537263, (47, 1866): 453.11886973683596, (47, 1867): 461.2380048579737, (47, 1868): 464.56520058969045, (47, 1870): 451.6090942918958, (47, 1871): 464.50538957543677, (47, 1875): 456.4755963063046, (47, 1880): 459.2418365818598, (47, 1882): 453.52174468137076, (47, 1883): 459.73628694904414, (47, 1889): 465.2416405081298, (47, 1893): 470.5164258810571, (47, 1894): 471.9593190644053, (47, 1899): 468.20178778410553, (47, 1900): 469.2320647076569, (47, 1902): 469.9319667680722, (47, 1905): 467.0095175211257, (47, 1907): 463.8067718515017, (47, 1910): 468.3705404754291, (47, 1917): 478.6896625368684, (47, 1920): 467.14980664646896, (47, 1935): 474.32081559970743, (47, 1937): 472.72466712138987, (47, 1946): 477.7349620133569, (47, 1949): 479.33926847213115, (47, 1950): 470.9377941375893, (47, 1951): 472.8562489628197, (47, 1952): 462.5102858903256, (47, 1953): 471.4918440964416, (47, 1954): 465.04411091098166, (47, 1958): 475.2901632795165, (47, 1960): 472.2959048125339, (47, 1968): 471.14883018527127, (47, 1969): 481.69203928580146, (47, 1974): 478.23610534153596, (47, 1975): 475.7433163939722, (47, 1979): 480.93411137780924, (47, 1980): 473.49915836995484, (47, 1981): 478.10524298195696, (47, 1985): 480.1145217468816, (47, 1994): 454.1843417711027, (47, 2011): 450.9904462008631, (47, 2019): 439.3378141765513, (47, 2020): 440.7565655004127, (47, 2029): 439.09026914906684, (47, 2030): 441.8682970157432, (47, 2032): 435.1019598215413, (47, 2033): 439.58974895306744, (47, 2034): 435.92873716649626, (47, 2036): 420.5040264816753, (47, 2037): 425.0132279850797, (47, 2038): 442.179215097591, (47, 2042): 437.58358897425825, (47, 2050): 445.15022976835695, (47, 2051): 441.2829339169431, (47, 2053): 442.87202530210493, (47, 2054): 442.27202120113554, (47, 2066): 442.81874568745974, (47, 2067): 444.83632115777726, (47, 2071): 457.34226550667296, (47, 2072): 459.27084531103907, (47, 2073): 472.2303397296472, (47, 2074): 469.8713457203985, (47, 2080): 465.47885670846136, (47, 2082): 459.4520810804665, (47, 2083): 460.73040487441745, (47, 2089): 464.34065717358834, (47, 2090): 466.1854946101556, (47, 2092): 468.8556304462324, (47, 2098): 469.8159363361068, (47, 2099): 466.92507948842393, (47, 2101): 466.4762742842308, (47, 2102): 468.6040937201357, (47, 2103): 466.4800020911015, (47, 2104): 463.70547844443564, (47, 2106): 458.98121446056393, (47, 2112): 463.513701599484, (47, 2113): 466.81465426718404, (47, 2114): 461.42051521032465, (47, 2117): 456.3261218046854, (47, 2123): 591.6314874958608, (47, 2124): 592.1520076272152, (47, 2134): 581.500518604235, (47, 2138): 586.6677464175696, (47, 2141): 584.5012036352732, (47, 2148): 549.5243200099103, (47, 2150): 581.6603915495676, (47, 2151): 579.5190056392265, (47, 2152): 578.9873396261339, (47, 2153): 553.0929125845283, (47, 2154): 553.4126733862374, (47, 2155): 547.1869273012119, (47, 2156): 551.1805608660911, (47, 2157): 529.64046645978, (47, 2160): 570.202981850926, (47, 2161): 575.3736282565716, (47, 2162): 539.648282892564, (47, 2163): 540.1730634625956, (47, 2164): 537.9616896515217, (47, 2168): 563.5406223549136, (47, 2172): 547.6011905549908, (47, 2174): 574.9738260234818, (47, 2178): 543.1721684729374, (47, 2179): 541.5315155733143, (47, 2183): 582.4976712357113, (47, 2185): 580.322171451704, (47, 2186): 581.081720819683, (47, 2190): 574.2142865108627, (47, 2192): 574.793185943265, (47, 2193): 583.8795828357011, (47, 2194): 584.4829534216294, (47, 2195): 579.8381298827529, (47, 2197): 572.3486287682679, (47, 2205): 566.5158108855468, (47, 2207): 560.5245570567436, (47, 2208): 562.9176282573974, (47, 2212): 594.0964260852053, (47, 2214): 528.6116290430346, (47, 2225): 513.5829081330663, (47, 2231): 615.8856041151068, (47, 2278): 477.04434280145847, (47, 2284): 468.42165483512315, (47, 2285): 465.44505986628485, (47, 2291): 447.0751031314161, (47, 2292): 471.61041810928816, (47, 2307): 468.4406381306499, (47, 2313): 439.6620091599042, (47, 2317): 482.62076946588485, (47, 2319): 468.73103494831463, (47, 2321): 464.06988706044274, (47, 2323): 471.1428158931203, (47, 2326): 482.3862051307891, (47, 2327): 482.8124224071998, (47, 2329): 482.39749969777824, (47, 2330): 480.28928160053067, (47, 2332): 476.22977252513425, (47, 2344): 487.53914967386606, (47, 2346): 482.66850546850793, (47, 2361): 523.7764879479975, (47, 2368): 496.27502235356474, (47, 2374): 492.30719858477437, (47, 2375): 494.7091143332747, (47, 2377): 499.18045613249427, (47, 2378): 492.497681090525, (47, 2379): 487.5386339391567, (47, 2380): 490.97996150972756, (47, 2383): 501.8844609753537, (47, 2385): 503.44485017049146, (47, 2395): 507.81267654469997, (47, 2397): 485.39649727015035, (47, 2398): 500.15559809905574, (47, 2399): 501.89307141952287, (47, 2400): 502.11397908531904, (47, 2402): 487.5211784970867, (47, 2403): 486.8964100935864, (47, 2404): 488.7627167227739, (47, 2405): 488.47362960325034, (47, 2407): 491.6321189369552, (47, 2408): 488.8283340605446, (47, 2409): 489.31871204595603, (47, 2411): 478.690025499805, (47, 2412): 481.9297304506929, (47, 2413): 480.3050987386401, (47, 2414): 480.00462424058554, (47, 2422): 476.01159218374937, (47, 2424): 483.55880394673653, (47, 2426): 485.09958591435833, (47, 2433): 482.9808754876899, (47, 2436): 477.9026002933946, (47, 2437): 483.3491609623172, (47, 2440): 483.5451118142987, (47, 2445): 429.99332883646093, (47, 2447): 434.71171182400724, (47, 2454): 434.72655453352155, (47, 2455): 438.60604883051803, (47, 2460): 434.14024208768944, (47, 2461): 433.71463750724405, (47, 2471): 414.6917828861186, (47, 2492): 260.768299847221, (47, 2511): 286.2028530192008, (47, 2523): 272.05565444051894, (47, 2525): 263.9066523178616, (47, 2535): 344.09490051292937, (47, 2537): 341.7680844645348, (47, 2538): 347.2563426987814, (47, 2539): 328.03627066185743, (47, 2540): 344.7053540012541, (47, 2542): 339.81733847832214, (47, 2559): 399.30274710026663, (47, 2575): 374.82828382680054, (47, 2599): 411.1142890235663, (47, 2600): 396.76969388425675, (47, 2607): 419.6557041248828, (47, 2627): 218.69032969421102, (47, 2647): 208.32675709047723, (47, 2674): 227.0479204561883, (47, 2681): 216.95745129102872, (47, 2683): 222.47863482060234, (47, 2686): 226.03169324123584, (47, 2689): 259.20303350832086, (47, 2690): 257.7029877254489, (47, 2713): 227.55737517172483, (47, 2714): 224.48573185411914, (47, 2715): 227.1562996266647, (47, 2739): 226.1303876977202, (47, 2740): 224.7437028908933, (47, 2741): 227.10914455296987, (47, 2749): 217.75603112346468, (47, 2750): 220.1366006009503, (47, 2752): 222.75415685108297, (47, 2755): 223.8905731001707, (47, 2758): 221.99890753349982, (47, 2759): 222.68421675034475, (47, 2769): 221.34938810151647, (47, 2771): 224.53392260680354, (47, 2779): 212.1030510763003, (47, 2784): 177.7473221118008, (47, 2800): 172.12497086426882, (47, 2802): 212.1724216623411, (47, 2803): 213.07125170661467, (47, 2804): 212.20544630151883, (47, 2805): 209.01037024740373, (47, 2807): 210.5675615209637, (47, 2809): 205.85611492794598, (47, 2812): 194.639948314675, (47, 2814): 194.9182971355724, (47, 2817): 185.11069183287404, (47, 2819): 215.23321420247936, (47, 2823): 181.35917730521268, (47, 2832): 209.80485666193184, (47, 2836): 198.72796374582526, (47, 2839): 212.30792202240212, (47, 2841): 190.4947222369325, (47, 2843): 191.5212628967963, (47, 2846): 194.39273746591044, (47, 2849): 208.92308160182324, (47, 2852): 207.3353391889939, (47, 2853): 209.58045333315468, (47, 2876): 204.23741969037636, (47, 2877): 213.0387834232463, (47, 2885): 206.8624929486746, (47, 2918): 228.67032526423483, (47, 2921): 229.80335332986178, (47, 2925): 233.35774048917668, (47, 2926): 240.41761994713613, (47, 2930): 215.65575866211032, (47, 2931): 228.3518666911253, (47, 2938): 225.2661651878466, (47, 2940): 251.78626040971608, (47, 2947): 245.5221105190776, (47, 2949): 223.50882613212943, (47, 2950): 221.5226664348513, (47, 2952): 219.746349776928, (47, 2958): 220.86102482054258, (47, 2959): 226.5541964253449, (47, 2960): 228.85637939698495, (47, 2961): 225.4785620540227, (47, 2963): 217.4269244826899, (47, 2968): 216.4404154109756, (47, 2976): 219.1248380928798, (47, 2981): 162.07403788971607, (47, 2982): 157.0381116058365, (47, 2984): 154.3885865430092, (47, 3003): 146.9432545057206, (47, 3046): 186.3741129516341, (47, 3050): 169.3598863037142, (47, 3051): 172.36749793897792, (47, 3053): 167.17548723173107, (47, 3069): 178.4304399894076, (47, 3071): 178.22226873569923, (47, 3080): 204.70440727455752, (47, 3199): 120.66170532919777, (47, 3200): 114.13719907755363, (47, 3205): 145.74734184416036, (47, 3209): 116.40870824846843, (47, 3215): 115.83440215321484, (47, 3217): 109.54813219063676, (47, 3249): 117.97438850353781, (47, 3263): 166.41681366844625, (47, 3289): 137.31878944417116, (47, 3301): 134.8106429005677, (47, 3302): 133.9610769117018, (47, 3307): 131.58267741846342, (47, 3310): 137.526393151775, (47, 3391): 182.3543005731551, (47, 3509): 936.9099529288939, (47, 3510): 941.4905661165271, (47, 3511): 939.1795035735195, (47, 3512): 942.6727768487881, (47, 3514): 942.3249694905297, (47, 3519): 922.7948178822312, (47, 3536): 930.1616426006002, (47, 3545): 923.7888922736379, (47, 3548): 931.8466840690477, (47, 3572): 926.6384345763729, (47, 3581): 929.8078718580024, (47, 3583): 935.8863073936506, (47, 3601): 913.1857672809721, (47, 3656): 918.4749537517482, (47, 3669): 923.8492825958054, (47, 3670): 919.5685871880903, (47, 3695): 944.6260952809452, (47, 3696): 941.4062441653614, (47, 3782): 947.4940839106926, (47, 3792): 949.3887200329481, (47, 3989): 2869.1956264227906, (47, 4008): 2891.5929997834205, (47, 4031): 2885.545824811011, (47, 4045): 2881.9735884730917, (47, 4144): 2887.4474737397004, (47, 4145): 2869.4741089304443, (47, 4164): 2879.864582283205, (47, 4168): 2874.9944088628026, (47, 4173): 2874.621021446436, (47, 4181): 2860.9109280262096, (47, 4228): 2843.178292507094, (47, 4248): 2843.995674768252, (47, 4254): 2739.037370327094, (47, 4260): 2737.65328245573, (47, 4262): 2746.8259761883, (47, 4273): 2743.9055056025495, (47, 4319): 2677.345391556218, (47, 4326): 2674.4709013814795, (47, 4328): 2675.009430046165, (47, 4334): 2680.996313699641, (47, 4335): 2679.478842216091, (47, 4372): 2634.124433017094, (47, 4413): 2707.470539877912, (47, 4434): 2631.653184858421, (47, 4447): 2643.770640664353, (47, 4452): 2632.3739197346263, (47, 4463): 2462.155655404019, (47, 4465): 2468.381841651171, (47, 4619): 2708.5703190962186, (47, 4645): 2727.292077022528, (47, 4657): 2723.5015378790877, (47, 4666): 2715.7794516395315, (47, 4676): 2728.011985784025, (47, 4678): 2731.2379325806155, (47, 4689): 2721.650804974302, (47, 4704): 2782.1863671932238, (47, 4726): 2902.8210364919846, (47, 4727): 2900.4907145768175, (47, 4730): 2896.0689388251603, (47, 4731): 2896.690278467273, (47, 4734): 2902.929177182383, (47, 4735): 2900.1654621182283, (47, 4736): 2900.7992876764524, (47, 4737): 2896.2227587127377, (47, 4738): 2896.356683914669, (47, 4756): 2898.3920049275844, (47, 4760): 2889.4000027198995, (47, 4761): 2891.807193481326, (47, 4762): 2885.5478294417508, (47, 4765): 2890.2243415898147, (47, 4773): 2907.9535872427737, (47, 4774): 2904.9035691500717, (47, 4790): 2906.549829272048, (47, 4795): 2904.75598427266, (47, 4799): 2905.396584600579, (47, 4801): 2908.9433355140727, (47, 4804): 2906.7584645107804, (47, 4805): 2905.2689218996866, (47, 4806): 2902.585166269541, (47, 4815): 2899.4955036347696, (47, 4816): 2905.775030653051, (47, 4817): 2905.8046601161727, (47, 4826): 2902.675770210284, (47, 4830): 2898.8867415420095, (47, 4839): 2896.1453445605835, (47, 4840): 2897.756628222721, (47, 4841): 2892.4557839100166, (47, 4846): 2891.0238157145254, (47, 4848): 2889.544523381265, (47, 4850): 2891.5028506549043, (47, 4871): 2868.723843378004, (47, 4883): 2888.1437515263624, (47, 4900): 2879.474474932287, (47, 4901): 2875.8210204985276, (47, 4917): 2689.500521763452, (47, 4931): 2671.312831456227, (47, 4944): 2692.2811409023366, (47, 4956): 2673.9308014877583, (47, 4958): 2671.9826523077422, (47, 4959): 2667.5543962615493, (47, 4961): 2678.1937288134027, (47, 4966): 2668.662394804654, (47, 5207): 2648.3625420908947, (47, 5272): 2341.9677402539432, (47, 5283): 2348.260309673398, (47, 5287): 2355.4671639350386, (47, 5289): 2358.1168311222987, (47, 5293): 2345.864341416243, (47, 5295): 2363.8875277722277, (47, 5296): 2362.0440344029585, (47, 5298): 2360.871021772002, (47, 5303): 2364.7098949335095, (47, 5305): 2334.911941890443, (47, 5306): 2327.4711636239476, (47, 5307): 2331.436306547158, (47, 5308): 2337.2982540383264, (47, 5313): 2339.2025707378257, (47, 5314): 2343.900567430388, (47, 5317): 2336.208038804202, (47, 5319): 2358.096843162904, (47, 5324): 2355.786470524101, (47, 5326): 2354.397412846996, (47, 5348): 2324.48811031684, (47, 5351): 2326.784280964977, (47, 5399): 2359.2032350179607, (47, 5413): 2331.05818246335, (47, 5422): 2364.4093300063687, (47, 5445): 2348.9348445041874, (47, 5448): 2342.7801207899597, (47, 5456): 2339.4904892876766, (47, 5467): 2344.7165548523917, (47, 5624): 2282.9140944606606, (47, 5671): 2506.2828030071455, (47, 5672): 2498.0123720559486, (47, 5797): 2606.024385385466, (47, 5871): 2428.9225670399715, (47, 5976): 2355.5542737233013, (47, 6118): 402.09976232915915, (47, 6248): 392.2247906457249, (47, 6345): 1962.7989764072602, (47, 6352): 1940.8314080072369, (47, 6354): 1968.2126235617834, (47, 6359): 1972.4820572246695, (47, 6376): 1944.2042530285844, (47, 6378): 1965.5977107578658, (47, 6381): 1970.6399208666335, (47, 6383): 1958.1643537172688, (47, 6396): 1967.9944245183942, (47, 6399): 1963.0026370511282, (47, 6408): 1941.6841779719334, (47, 6409): 1952.2473434604976, (47, 6419): 1917.1470412879085, (47, 6422): 1944.7286438468614, (47, 6423): 1942.966224410272, (47, 6424): 1966.3368588527858, (47, 6439): 1962.2121781608616, (47, 6464): 1956.21383339063, (47, 6465): 1953.9043605722964, (47, 6469): 1956.4477695947141, (47, 6470): 1955.0591633374534, (47, 6472): 1979.9021958754597, (47, 6480): 1975.7804158041938, (47, 6486): 1989.6813417388432, (47, 6497): 1985.0220459449815, (47, 6503): 1958.621953337227, (47, 6508): 1959.6106743803175, (47, 6509): 1964.134945525739, (47, 6521): 1978.8300375384708, (47, 6544): 1977.838861466723, (47, 6552): 1949.1508119629027, (47, 6553): 1945.7726999990707, (47, 6554): 1942.3290479306454, (47, 6578): 1954.7261703001623, (47, 6582): 1952.7604901426846, (47, 6601): 1956.3830294118845, (47, 6609): 1983.1776705705872, (47, 6610): 1984.2461713169066, (47, 6611): 1984.6680545293277, (47, 6614): 1982.7564229986426, (47, 6615): 1983.4645164714925, (47, 6616): 1987.3437575958515, (47, 6617): 1985.6648853014956, (47, 6618): 1991.0507553567202, (47, 6619): 1980.3255111842493, (47, 6620): 1987.5892426599924, (47, 6621): 1984.7236144816293, (47, 6622): 1985.281265955505, (47, 6623): 1982.6031245846066, (47, 6624): 1980.1806539684526, (47, 6625): 1979.550331569236, (47, 6626): 1980.1020802356322, (47, 6627): 1981.9241755811545, (47, 6628): 1987.1732111582419, (47, 6629): 1981.1924231314083, (47, 6630): 1976.8166241306863, (47, 6632): 1980.8001964628018, (47, 6634): 1973.7691982221716, (47, 6635): 1983.5848723055378, (47, 6636): 1987.5654808154284, (47, 6637): 1977.2238519123555, (47, 6638): 1977.3086094335122, (47, 6639): 1982.3023610282542, (47, 6640): 1977.7234047900836, (47, 6641): 1984.7924504469015, (47, 6642): 1977.477436964508, (47, 6643): 1979.6771557767017, (47, 6645): 1980.7978046669111, (47, 6646): 1989.8668293185283, (47, 6647): 1978.296121113943, (47, 6653): 1983.2888446517861, (47, 6655): 1982.2917903413154, (47, 6658): 1973.6110694044678, (47, 6662): 1977.4236968673365, (47, 6819): 1814.245231512691, (47, 6996): 1876.433961291993, (47, 7059): 1915.0946368462094, (47, 7187): 1870.108145148268, (47, 7304): 1774.2319758086005, (47, 7528): 1881.0515988170748, (47, 7720): 2104.1338490977164, (47, 7793): 2102.3611016135287, (47, 7807): 2104.523903238906, (47, 7808): 2101.9364280094414, (47, 7831): 2005.7285369418148, (47, 7850): 2041.5625110436235, (47, 7852): 2032.8257140556802, (47, 8012): 2089.4597796002818, (47, 8125): 2143.7715856610657, (47, 8208): 2175.6511426044685, (47, 8392): 2039.1850104574994, (47, 8651): 1628.23018229466, (47, 9088): 1797.3821931004595, (47, 9443): 1570.4063787490234, (47, 9444): 1576.5562930768583, (47, 9828): 1428.5202159034723, (47, 9868): 1399.3769085085505, (47, 10180): 2149.133548902449, (47, 10256): 2249.6103472704563, (47, 10276): 2200.5196272254348, (47, 10378): 2204.501313616898, (47, 10676): 2130.873637641265, (47, 10714): 2070.2968147668835, (47, 10730): 2070.426178864806, (47, 10862): 2115.768129962333, (47, 10881): 2131.2903877021513, (47, 10883): 2129.3782798895286, (47, 10885): 2112.478942327965, (47, 10891): 2126.428135235842, (47, 10909): 2125.5202197581375, (47, 10911): 2128.166808869272, (47, 10913): 2124.4326357499267, (47, 10915): 2124.513817301085, (47, 10919): 2126.877750800476, (47, 11037): 2017.219978661917, (47, 11039): 1979.636978458957, (47, 11516): 3060.453436733015, (47, 11856): 2683.3751340168346, (47, 11857): 2681.258138879308, (47, 11861): 2682.4843638450243, (47, 11881): 2676.4619373847627, (47, 11902): 2659.5728541140593, (47, 11911): 2655.0531702354288, (47, 11914): 2658.039280935234, (47, 11922): 2671.096281295938, (47, 11924): 2674.7015894562505, (47, 11926): 2669.7503836371984, (47, 11950): 2677.7288554538, (47, 11963): 2693.8537488565435, (47, 11983): 2680.2387095826743, (47, 11985): 2702.081228657895, (47, 12009): 2696.570494614048, (47, 12010): 2685.733343908537, (47, 12018): 2687.29127186799, (47, 12020): 2690.737733338507, (47, 12021): 2692.3651376475327, (47, 12024): 2703.2760112044543, (47, 12025): 2700.077088997562, (47, 12027): 2697.372711907427, (47, 12031): 2683.837676470152, (47, 12032): 2688.012560996649, (47, 12035): 2695.2866356893855, (47, 12041): 2704.8295873356483, (47, 12045): 2550.9156388684896, (47, 12145): 2618.167235898167, (47, 12275): 2870.035435647318, (47, 12294): 2837.32520547987, (47, 12358): 2924.265291468907, (47, 12463): 2955.730961196411, (47, 12465): 2954.4831455738354, (47, 12482): 2972.87004621171, (47, 12503): 2969.9790949709623, (47, 12506): 2974.2405348133752, (47, 12549): 2968.5359708646893, (47, 12559): 2964.584146969934, (47, 12569): 2966.830494701292, (47, 12572): 2970.1070870900476, (47, 12574): 2963.648112845152, (47, 12576): 2972.6644794400922, (47, 12591): 2973.905281880192, (47, 12608): 3001.333792995481, (47, 12696): 2961.047595261868, (47, 12710): 2988.001524744058, (47, 12728): 2973.3185658863663, (47, 12766): 2285.564076706494, (47, 12771): 2261.823243381781, (47, 12790): 2257.483413260275, (47, 12795): 2246.6567001488174, (47, 12797): 2211.830032635106, (47, 12798): 2217.437414204774, (47, 12811): 2248.0601867333844, (47, 12830): 2236.488195571711, (47, 12848): 2244.4812718629946, (47, 12850): 2248.6627414493605, (47, 12852): 2235.818470121366, (47, 12854): 2231.093429651066, (47, 12859): 2249.878271828929, (47, 12861): 2223.2567023229158, (47, 12865): 2252.7047635248077, (47, 12866): 2251.0454598935557, (47, 12867): 2259.82089957578, (47, 12874): 2255.455712756354, (47, 12875): 2259.364036184136, (47, 12881): 2243.80780654287, (47, 12883): 2249.745471486601, (47, 12885): 2262.293797639114, (47, 12888): 2247.543180475444, (47, 12889): 2246.7269202137454, (47, 12892): 2256.1740603656262, (47, 12893): 2247.2284330452662, (47, 12896): 2250.585523288307, (47, 12906): 2253.439010833025, (47, 13018): 2197.7870884183044, (47, 13071): 2195.561018017694, (47, 13131): 2168.3645803898416, (47, 13146): 2202.2075422148637, (47, 13159): 2144.4787536044682, (47, 13193): 2163.0856590765957, (47, 13198): 2112.638688006424, (47, 13292): 2177.4887757786664, (47, 13296): 2200.8015402148926, (47, 13406): 2070.3673153658137, (47, 13407): 2067.9557313776104, (47, 13417): 2059.1866621682075, (47, 13418): 2064.464681870098, (47, 13438): 2092.3665575809528, (47, 13442): 2098.73267867724, (47, 13443): 2093.847377990661, (47, 13764): 1658.8191262581804, (47, 13766): 1665.0042069286221, (47, 13771): 1658.388375477022, (47, 13783): 1654.7273963407094, (47, 13784): 1672.0141274937341, (47, 13792): 1645.6860300339818, (47, 13824): 1650.3466746681793, (47, 14017): 1691.5033282718134, (47, 14870): 2125.2814822364303, (47, 14997): 1843.9328564369016, (47, 15000): 1846.1543967600571, (47, 15003): 1851.8982093013876, (47, 15006): 1854.0049980543902, (47, 15007): 1858.3225172143989, (47, 15056): 1862.57573123714, (47, 15063): 1859.8257717524941, (47, 15069): 1860.3125684500978, (47, 15076): 1860.0977829495307, (47, 15086): 1845.0369528903977, (47, 15087): 1842.7572180515965, (47, 15111): 1828.7048363492693, (47, 15116): 1836.9327298280587, (47, 15722): 1725.649277127884, (47, 15998): 1697.8919046476824, (47, 16073): 843.1652123289033, (47, 16939): 416.30293632306774, (47, 16940): 421.13034205358724, (47, 16951): 404.464771722106, (47, 16963): 406.7464739472005, (47, 16965): 405.8257362692119, (47, 16969): 400.17503900156953, (47, 16970): 408.57391230432825, (47, 16971): 409.86995647384896, (47, 16973): 405.97595641854474, (47, 16974): 401.5890334241724, (47, 16976): 411.0439713510987, (47, 16978): 413.3610938565736, (47, 16980): 414.0840084893452, (47, 16982): 397.3556562473572, (47, 17045): 3.607470959331592, (47, 17048): 6.7284161737706, (47, 17304): 2816.560125081489, (47, 17305): 2810.0012651281027, (47, 17330): 2814.6579949916213, (47, 17334): 2809.049271394548, (47, 17343): 2820.1205625563025, (47, 17345): 2806.162930483585, (47, 17347): 2812.4088327752393, (47, 17351): 2798.2514076396224, (47, 17372): 2807.182982450182, (47, 17373): 2820.050363627299, (47, 17377): 2820.74072319351, (47, 17382): 2811.8132878938795, (47, 17383): 2814.343294986906, (47, 17389): 2808.8630943942344, (47, 17400): 2818.3786629262067, (47, 17401): 2818.6119099903126, (47, 17402): 2818.6565977297687, (47, 17403): 2819.3364802003402, (47, 17440): 2803.87826122191, (47, 17455): 2816.8368555892635, (47, 17491): 2815.752604471843, (47, 17507): 2809.6011065908397, (47, 17509): 2815.3247522067422, (47, 17590): 2791.962310817683, (47, 17615): 2780.159640166139, (47, 17642): 2783.999412542587, (47, 17643): 2782.5876854288576, (47, 17668): 2780.5584684692835, (47, 17721): 2773.945142449603, (47, 17754): 2823.629514562529, (47, 17769): 2814.1829566693414, (47, 17776): 2789.25647845172, (47, 17804): 2822.921360567243, (47, 17809): 2828.054666493382, (47, 17824): 2826.310286180119, (47, 17837): 2803.8730341327932, (47, 17838): 2802.9706979341445, (47, 17862): 2798.4596629309694, (47, 17866): 2810.0640938131914, (47, 17872): 2795.668045157626, (47, 17873): 2786.474941674306, (47, 17881): 2800.363031260457, (47, 17947): 924.26900000297, (47, 17951): 927.7768140574062, (47, 17953): 931.3228965317943, (47, 17954): 932.9477228121108, (47, 17959): 920.0121490784767, (47, 17963): 916.3234390309897, (47, 18000): 945.1317970407737, (47, 18001): 947.6963341935766, (47, 18111): 1037.883970387499, (47, 18148): 1153.938959248359, (47, 18166): 1117.4560178006227, (47, 18189): 1057.2771227427365, (47, 18239): 2823.6370010070154, (47, 18240): 2823.2532226238586, (47, 18245): 2823.9489300310406, (47, 18247): 2822.48396430539, (47, 18251): 2823.536569259709, (47, 18256): 2824.300816323296, (47, 18258): 2822.8285075654735, (47, 18259): 2822.885665029859, (47, 18260): 2823.1407076478067, (47, 18262): 2823.864117514226, (47, 18263): 2824.4536972864075, (47, 18264): 2824.728153343545, (47, 18266): 2823.9563266311297, (47, 18267): 2824.2702675952164, (47, 18268): 2824.3032866024378, (47, 18269): 2824.894039521734, (47, 18275): 2824.613892573435, (47, 18285): 2824.7625771377934, (47, 18308): 2818.4959664135777, (47, 18313): 2815.460656732366, (47, 18314): 2815.844371421518, (47, 18315): 2825.7620349455538, (47, 18316): 2825.2672236742033, (47, 18317): 2825.5161879722978, (47, 18320): 2826.3810218017975, (47, 18321): 2826.321477265781, (47, 18322): 2826.802294711753, (47, 18324): 2827.815213974676, (47, 18325): 2829.915793167317, (47, 18326): 2829.1532065438328, (47, 18327): 2825.3797684260207, (47, 18329): 2831.345187341771, (47, 18330): 2828.940593036226, (47, 18331): 2827.749181129459, (47, 18332): 2826.2970429915854, (47, 18333): 2829.109079122351, (47, 18336): 2828.581087460666, (47, 18337): 2829.572288286419, (47, 18403): 2826.060321279148, (47, 18432): 2784.662299753432, (47, 18451): 2812.664331888188, (47, 18466): 2841.049552776621, (47, 18481): 2827.4560828387816, (47, 18483): 2827.1508796654502, (47, 18484): 2826.2280160772857, (47, 18485): 2823.7549233735645, (47, 18486): 2827.932547337051, (47, 18487): 2825.6063303328774, (47, 18489): 2826.5871712279627, (47, 18490): 2830.0912330761603, (47, 18491): 2831.3585172780986, (47, 18492): 2822.6466620991773, (47, 18493): 2827.840893480192, (47, 18494): 2825.8277215619564, (47, 18495): 2829.1920735743793, (47, 18496): 2827.616552249744, (47, 18497): 2825.3479878546177, (47, 18498): 2824.743018021432, (47, 18499): 2826.6032992308064, (47, 18501): 2825.7883288961975, (47, 18502): 2824.632230938768, (47, 18503): 2823.379434771826, (47, 18504): 2827.7693353875397, (47, 18506): 2826.828433082865, (47, 18507): 2825.895626233657, (47, 18508): 2826.636141725227, (47, 18509): 2826.945084268561, (47, 18510): 2823.8293179840707, (47, 18511): 2828.812134810851, (47, 18512): 2826.8337980260253, (47, 18515): 2828.3098974379486, (47, 18516): 2829.390881685202, (47, 18517): 2828.358547346854, (47, 18518): 2830.113569673123, (47, 18519): 2827.8537451119923, (47, 18520): 2825.924040064307, (47, 18522): 2832.3586074303953, (47, 18523): 2832.9539807487936, (47, 18532): 2835.115431146424, (47, 18535): 2830.962189456787, (47, 18537): 2828.649963954171, (47, 18539): 2829.3046065405815, (47, 18540): 2829.7545812943363, (47, 18541): 2831.042080710749, (47, 18542): 2831.828351189068, (47, 18543): 2828.0560805973696, (47, 18546): 2830.402620206874, (47, 18555): 2834.0574507204547, (47, 18556): 2834.9442771928825, (47, 18565): 2835.286046281639, (47, 18567): 2836.992589352904, (47, 18568): 2834.726803655053, (47, 18577): 2848.8829593135124, (47, 18583): 2845.6137867326847, (47, 18605): 2847.514610031398, (47, 18608): 2839.507014404319, (47, 18616): 2860.799376621957, (47, 18618): 2872.672296608258, (47, 18625): 2866.436745263411, (47, 18645): 2855.48166078029, (47, 18646): 2858.8686026167325, (47, 18653): 2851.7177369960477, (47, 18654): 2860.897723451702, (47, 18655): 2855.3498013772664, (47, 18666): 2888.058706857138, (47, 18837): 2811.940146620534, (47, 18974): 2804.8436051494305, (47, 18999): 2810.231050496797, (47, 19000): 2813.5460003617727, (47, 19174): 2635.5379209458565, (47, 19342): 2696.47625944924, (47, 19455): 2674.9223256224655, (47, 19555): 2503.4164011667976, (47, 19564): 2506.4320631513606, (47, 19573): 2500.8494115170415, (47, 19586): 2498.7933812971073, (47, 19605): 2502.4891455020493, (47, 19611): 2506.518468355736, (47, 19614): 2506.5095655865016, (47, 19641): 2582.1262781598707, (47, 19702): 2578.7071681483394, (47, 19713): 2573.601423080493, (47, 19731): 2486.390067498991, (47, 19819): 2645.5886917032803, (47, 19893): 2540.8031494482952, (47, 19899): 2579.0730545223805, (47, 19929): 2550.5618007274606, (47, 19951): 2625.713652408835, (47, 19962): 2557.261838343413, (47, 19970): 2572.6539215152993, (47, 19971): 2573.264950669017, (47, 19972): 2567.120407450078, (47, 19975): 2563.953667120341, (47, 19978): 2640.675667915724, (47, 19987): 2641.836178090426, (47, 19989): 2621.1274020517944, (47, 20039): 2645.5812789633874, (47, 20043): 2654.057937671026, (47, 20047): 2647.2741347084916, (47, 20052): 2624.5028915177345, (47, 20054): 2626.396147531095, (47, 20085): 2729.183378768374, (47, 20104): 2735.6427825326446, (47, 20132): 2696.25296002157, (47, 20203): 2538.764975420571, (47, 20280): 2530.791856645414, (47, 20285): 2528.8376211995414, (47, 20290): 2534.31747945249, (47, 20297): 2527.269120792224, (47, 20309): 2647.1821020202433, (47, 20453): 2753.753008279827, (47, 20485): 2482.947304899497, (47, 20520): 2465.033343982694, (47, 20526): 2458.89682725418, (47, 20698): 1483.6335008291874, (47, 20868): 1272.6950389944184, (47, 21042): 2280.312344118716, (47, 21057): 2321.985077851155, (47, 21066): 2302.965428051669, (47, 21075): 2293.090541975072, (47, 21093): 2285.4244176793727, (47, 21098): 2317.901085041877, (47, 21127): 2284.7928912063385, (47, 21130): 2293.6278270824323, (47, 21144): 2290.583735157423, (47, 21146): 2282.057702865547, (47, 21147): 2289.329362652989, (47, 21148): 2297.228368506544, (47, 21153): 2272.7048562444375, (47, 21293): 2352.00749400445, (47, 21426): 2323.618591245089, (47, 21442): 2364.884341922844, (47, 21451): 2368.947808436903, (47, 21466): 2345.076562705619, (47, 21469): 2352.063607753136, (47, 21471): 2341.4944511661415, (47, 21473): 2347.4870295658625, (47, 21475): 2342.3663511184286, (47, 21482): 2355.754507592642, (47, 21484): 2354.6806911143663, (47, 21488): 2350.387028250122, (47, 21494): 2343.3283968993624, (47, 21498): 2348.2787604435125, (47, 21500): 2341.237692445803, (47, 21514): 2358.5651557403116, (47, 21537): 2342.031724270282, (47, 21662): 2367.2451294182288, (47, 21691): 2340.717800663782, (47, 21757): 2285.9014863781044, (47, 21777): 2205.883466827746, (47, 21778): 2199.2223922992143, (47, 21779): 2203.8560698132765, (47, 21790): 2212.3983468181495, (47, 21802): 2213.82842165316, (47, 21824): 2221.653902750602, (47, 21874): 2206.7045350308563, (47, 21879): 2204.4572488081976, (47, 21983): 2223.363451992652, (47, 22002): 2301.3147364056267, (47, 22132): 2235.169630168212, (47, 22261): 1460.189278686328, (47, 22298): 1479.3809983637684, (47, 22339): 1440.6897233104974, (47, 22508): 1566.478970785517, (47, 22841): 521.075850848994, (47, 22842): 517.7125909937494, (47, 22874): 501.5820833454264, (47, 22941): 513.5659384776537, (47, 22956): 513.3774174722105, (47, 22960): 522.3167920115812, (47, 22968): 479.26119873614454, (47, 22970): 486.74025161208226, (47, 22974): 459.58804988721823, (47, 22980): 463.49983724277166, (47, 23025): 422.1938452203076, (47, 23028): 412.81545574903515, (47, 23081): 371.30979602797447, (47, 23104): 294.9921869128696, (47, 23147): 383.07578328002506, (47, 23298): 2479.7393609432147, (47, 23376): 2460.987100953648, (47, 23381): 2454.215783822855, (47, 23529): 2495.3485635865563, (47, 23556): 2483.9333064485786, (47, 23718): 2464.509802093079, (47, 24001): 2589.91007503415, (47, 24094): 2632.362225508976, (47, 24129): 2651.0234702705807, (47, 24174): 2615.3766963440057, (47, 24235): 2658.9092261634173, (47, 24259): 2674.6906060717697, (47, 24260): 2673.6675889783987, (47, 24261): 2669.363743108723, (47, 24305): 2695.1336955047877, (47, 24306): 2699.1656038354704, (47, 24307): 2693.478840389343, (47, 24308): 2631.004151244351, (47, 24498): 2735.87579632143, (47, 24499): 2736.4401202029744, (47, 24500): 2732.818698990383, (47, 24668): 2701.006536102662, (47, 24711): 2762.9328586858355, (47, 24756): 2778.6910784104425, (47, 24788): 2782.695378477678, (47, 24809): 2765.146010414444, (47, 24813): 2770.3343831745537, (47, 24821): 2768.4953559360606, (47, 24825): 2770.4413123062063, (47, 24832): 2763.491149477941, (47, 24833): 2766.5047245888204, (47, 24835): 2769.68390634048, (47, 24837): 2774.061653131047, (47, 24840): 2763.239286445018, (47, 24841): 2767.4507029919723, (47, 24844): 2763.6676100926015, (47, 24845): 2765.274758240599, (47, 24846): 2766.6155586398154, (47, 24849): 2768.3979072365064, (47, 24850): 2771.610554249664, (47, 24863): 2727.5991159942987, (47, 24866): 2732.87548395612, (47, 24885): 2740.2313756598214, (47, 24886): 2741.3317474037403, (47, 24889): 2750.829120254882, (47, 24903): 2754.373424185077, (47, 24909): 2733.217928884638, (47, 24999): 2956.933611699653, (47, 25019): 2948.0798200616796, (47, 25028): 2954.3995781122726, (47, 25137): 2547.526534167508, (47, 25145): 2554.9308473585343, (47, 25208): 2642.7082817933006, (47, 25233): 2632.729798900202, (47, 25371): 2546.0616143063453, (47, 25377): 2524.293002968463, (47, 25828): 2142.659643275186, (47, 25851): 2081.9183477565334, (47, 25874): 2137.7839848139506, (47, 25898): 2165.4809381263003, (47, 25946): 2136.5730526075117, (47, 26047): 2262.929337836341, (47, 26066): 2386.441699069248, (47, 26197): 2304.6790857086157, (47, 26212): 1969.95763382371, (47, 26253): 1952.9747594629073, (47, 26254): 1958.80715281662, (47, 26257): 1966.7816802586203, (47, 26258): 1956.9758973244643, (47, 26260): 1961.8644524412505, (47, 26266): 1950.7170089178142, (47, 26267): 1957.2382370720643, (47, 26271): 1958.0121220282715, (47, 26304): 2016.4534819369555, (47, 26305): 2014.5011714293903, (47, 26363): 2127.724842177847, (47, 26441): 1592.84571893884, (47, 26442): 1591.5257983937229, (47, 26450): 1598.8562090876023, (47, 26459): 1610.6484186155967, (47, 26462): 1614.6343759601484, (47, 26467): 1595.6028660198735, (47, 26471): 1595.116827824406, (47, 26472): 1593.995459878588, (47, 26473): 1592.5854259189755, (47, 26476): 1578.9946502109556, (47, 26485): 1601.7470398694898, (47, 26493): 1595.7499470160574, (47, 26524): 1616.8193290360152, (47, 26525): 1614.46412662583, (47, 26556): 1598.252634251726, (47, 26560): 1608.4154392218136, (47, 26561): 1614.727235935859, (47, 26564): 1597.4286212410648, (47, 26569): 1612.589543440177, (47, 26570): 1610.6169370330415, (47, 26573): 1604.5044976234606, (47, 26581): 1600.1679419848083, (47, 26583): 1604.3934155093375, (47, 26593): 1594.4536309146315, (47, 26837): 1589.670713357843, (47, 26844): 1587.5054800232883, (47, 26863): 1581.1984561327454, (47, 26893): 1570.1466816339614, (47, 26902): 1566.7732990103489, (47, 26905): 1580.2144402561344, (47, 26912): 1574.4275134337113, (47, 26921): 1576.5676521606897, (47, 26922): 1568.0803277278978, (47, 27212): 1811.7508348602973, (47, 27218): 1824.5750418909322, (47, 27239): 1805.9532895802874, (47, 27257): 1804.0428474189198, (47, 27274): 1803.116435479872, (47, 27279): 1799.3569315791958, (47, 27282): 1801.7007075128356, (47, 27283): 1808.784403954156, (47, 27285): 1799.5951449590516, (47, 27286): 1794.5124738166194, (47, 27290): 1803.0540712416978, (47, 27295): 1810.6405680012108, (47, 27300): 1804.3542451419744, (47, 27344): 1792.1235947024702, (47, 27366): 1785.35048529605, (47, 27383): 1790.710720851926, (47, 27398): 1798.042920161898, (47, 27406): 1803.3219100711765, (47, 27407): 1805.9810368559597, (47, 27426): 1836.9803431029634, (47, 27432): 1838.110660730249, (47, 27460): 1841.095766555789, (47, 27523): 1720.6551427804359, (47, 27545): 1755.2682001943535, (47, 27602): 1685.6263166347433, (47, 27606): 1690.6054123965773, (47, 27646): 1655.3441499029698, (47, 27667): 1641.1536018061665, (47, 27672): 1643.7178345526206, (47, 27674): 1644.0455703865578, (47, 27688): 1655.0436114247852, (47, 27692): 1637.5498219990704, (47, 27693): 1638.937720364985, (47, 27705): 1635.3022020060607, (47, 27712): 1631.4474033749987, (47, 27786): 1823.8723806763835, (47, 27790): 1874.682995212975, (47, 27791): 1881.8045110025248, (47, 27795): 1821.3617400035107, (47, 27801): 1854.90027751432, (47, 27813): 1817.4999643000021, (47, 27816): 1828.102516326349, (47, 27823): 1856.5939061851832, (47, 27830): 1840.3572559645304, (47, 27884): 1643.6860958712057, (47, 27885): 1655.7481867391998, (47, 27896): 1650.0892429536143, (47, 27919): 1653.1605121445584, (47, 27922): 1649.4902514467165, (47, 27930): 1649.8067375516346, (47, 27934): 1647.1538888223433, (47, 27935): 1643.9417939477653, (47, 27948): 1512.001727506442, (47, 27951): 1567.3306732778456, (47, 28061): 1211.6413512287925, (47, 28290): 1094.5991823528448, (47, 28292): 1076.6152759684064, (47, 28293): 1089.8173207308364, (47, 28295): 1080.4800494420017, (47, 28296): 1089.251690470039, (47, 28297): 1103.0192946432603, (47, 28302): 1094.5354602666487, (47, 28310): 504.7513886718034, (47, 28313): 500.34084750752436, (47, 28372): 496.8749250718393, (47, 28398): 496.2705236427796, (47, 28399): 498.9234323446046, (47, 28400): 494.7221502177254, (47, 28401): 505.6957319436269, (47, 28445): 505.71105901636224, (47, 28475): 515.1576404792385, (47, 28885): 2665.507610419221, (47, 28886): 2662.123113458515, (47, 28915): 2666.002009449865, (47, 28916): 2662.720691043393, (47, 28917): 2660.9471287140877, (47, 28921): 2672.000486218756, (47, 28931): 2671.2426869274645, (47, 28945): 2656.093035833035, (47, 28982): 2659.5894769044485, (47, 29219): 2683.9162903803317, (47, 29228): 2667.6083186440355, (47, 29246): 2775.056312756173, (47, 29248): 2774.1924387918198, (47, 29282): 2752.026640332176, (47, 29290): 2785.2086800051084, (47, 29291): 2780.968000743245, (47, 29292): 2785.0300232833383, (47, 29293): 2776.3926845905503, (47, 29294): 2783.530079599851, (47, 29298): 2777.2130524120707, (47, 29299): 2776.6418107667796, (47, 29304): 2768.199088415331, (47, 29317): 2747.2410304446244, (47, 29323): 2745.5934620921544, (47, 29330): 2755.72241079218, (47, 29331): 2760.6077210537155, (47, 29344): 2687.1184811513876, (47, 29445): 2503.131846626543, (47, 29724): 651.0802647089944, (47, 29738): 651.4432785157542, (47, 29745): 655.5929146319191, (47, 29748): 681.9645301152431, (47, 29750): 693.5388364558358, (47, 29759): 678.3080656425843, (47, 29772): 679.9940089266772, (47, 29781): 680.3607332297148, (47, 29784): 668.842284615097, (47, 29790): 685.3465263678648, (47, 29811): 695.9600593020452, (47, 29817): 767.2145486446586, (47, 29818): 767.9718621617051, (47, 29929): 639.133020940224, (47, 30039): 572.4185832191984, (47, 30066): 526.0941323061913, (47, 30116): 577.4890962224597, (47, 30238): 679.9448939348346, (47, 30248): 552.424355538293, (47, 30260): 544.7539481125517, (47, 30545): 2606.6200233412137, (47, 30733): 2429.3760115958207, (47, 30756): 2391.471116473197, (47, 30921): 2472.531380482211, (47, 31079): 1970.8481730992673, (47, 31149): 1961.1359559106934, (47, 31154): 1959.4453918714491, (47, 31160): 1960.1435369055218, (47, 31163): 1956.8565613533624, (47, 31189): 1893.5127596100874, (47, 31215): 1895.1866875220148, (47, 31259): 1876.9562477783447, (47, 31262): 1870.6645974420226, (47, 31430): 1971.4990791266937, (47, 31568): 1765.3824485034313, (47, 31751): 1929.4326794009305, (50, 109): 1728.2554195014668, (50, 872): 593.605615349696, (50, 873): 594.8093920380569, (50, 877): 590.5916069960638, (50, 879): 590.4105502120193, (50, 884): 580.7954168343347, (50, 889): 583.3331538022112, (50, 891): 581.4232938171509, (50, 892): 592.1860873144806, (50, 894): 593.5507926868994, (50, 896): 598.5789844079711, (50, 903): 586.3553352881517, (50, 909): 596.7681858411854, (50, 910): 600.6937602449406, (50, 912): 599.1869945937132, (50, 913): 596.2821939185364, (50, 916): 600.2187408826171, (50, 926): 605.6540220958866, (50, 927): 606.0785870798958, (50, 948): 581.6277015890286, (50, 961): 597.4206942373279, (50, 962): 599.9890639658256, (50, 963): 602.0889645073602, (50, 967): 588.4153370173822, (50, 974): 578.9877594725305, (50, 998): 585.8635615519604, (50, 1014): 680.1800834146704, (50, 1086): 694.1185637954047, (50, 1087): 706.7733643977618, (50, 1089): 699.3560685345269, (50, 1090): 698.6351708064892, (50, 1092): 699.8429506147696, (50, 1097): 696.3873189654469, (50, 1107): 708.5619148976181, (50, 1387): 1333.9061020157765, (50, 1554): 1409.9950199185857, (50, 1827): 688.1174526131864, (50, 1828): 689.8446958156233, (50, 1829): 689.9223691428324, (50, 1830): 683.7358184962277, (50, 1831): 685.1781632156761, (50, 1832): 685.0867284556027, (50, 1833): 686.0633136182555, (50, 1836): 686.447548062812, (50, 1841): 688.6905091754952, (50, 1843): 687.1866691540241, (50, 1844): 686.9586235900765, (50, 1845): 684.3782532021256, (50, 1847): 681.3033061932822, (50, 1848): 682.9415152879391, (50, 1849): 689.864656975091, (50, 1850): 691.5211982359609, (50, 1851): 681.7811393018117, (50, 1852): 679.823956167039, (50, 1854): 682.2715433049605, (50, 1856): 678.2663627044656, (50, 1857): 681.6758428404187, (50, 1858): 690.528591153162, (50, 1861): 688.0012456746875, (50, 1866): 676.3384880066804, (50, 1867): 690.5571426018241, (50, 1868): 691.0739187840718, (50, 1870): 684.117759593327, (50, 1871): 692.0529581303467, (50, 1875): 683.5952167772436, (50, 1880): 681.2217543466005, (50, 1882): 678.7255543997519, (50, 1883): 693.9439005235606, (50, 1889): 685.6831340681636, (50, 1893): 693.4873589512833, (50, 1894): 692.7662066090361, (50, 1899): 685.976856150836, (50, 1900): 687.6828684215577, (50, 1902): 695.8044251264588, (50, 1905): 696.1558046101061, (50, 1907): 686.3510109796198, (50, 1910): 689.6110306991287, (50, 1917): 706.7024578587561, (50, 1920): 688.3524063767794, (50, 1935): 700.4563004010582, (50, 1937): 701.2353727961251, (50, 1946): 687.9406879796362, (50, 1949): 690.7283418318827, (50, 1950): 679.3385083802704, (50, 1951): 683.6360565224006, (50, 1952): 680.2415418539307, (50, 1953): 686.3033891803315, (50, 1954): 681.182915968774, (50, 1958): 687.9031790448779, (50, 1960): 689.414917449554, (50, 1968): 690.034042322224, (50, 1969): 704.9364270517416, (50, 1974): 700.6637868357592, (50, 1975): 699.2516204602994, (50, 1979): 697.6634027578389, (50, 1980): 693.1460749070776, (50, 1981): 697.0363692055943, (50, 1985): 699.2425872535076, (50, 1994): 667.3304430678328, (50, 2011): 677.2650623479096, (50, 2019): 687.1188736047488, (50, 2020): 685.7438022913617, (50, 2029): 676.7829368436632, (50, 2030): 684.859314664231, (50, 2032): 673.3439373403701, (50, 2033): 680.0278189016802, (50, 2034): 678.0260326021364, (50, 2036): 661.7765816356895, (50, 2037): 666.2349095739687, (50, 2038): 675.9951393561465, (50, 2042): 697.9959736672756, (50, 2050): 681.8719936945648, (50, 2051): 679.4621630257188, (50, 2053): 680.9570838716725, (50, 2054): 682.8078673227009, (50, 2066): 678.6796426986061, (50, 2067): 679.7699648425516, (50, 2071): 664.9503807629742, (50, 2072): 670.1359728496328, (50, 2073): 666.2520908694721, (50, 2074): 664.3364807502834, (50, 2080): 654.8247834813338, (50, 2082): 672.4426942561431, (50, 2083): 675.2629273883176, (50, 2089): 672.8068055911762, (50, 2090): 675.8072721530494, (50, 2092): 674.6354521845391, (50, 2098): 660.0091328848372, (50, 2099): 660.7454095306884, (50, 2101): 657.6461731724992, (50, 2102): 670.0831217153735, (50, 2103): 665.3609620901033, (50, 2104): 661.8502311108805, (50, 2106): 675.7167670229678, (50, 2112): 657.4470486035437, (50, 2113): 670.6555734926422, (50, 2114): 670.3115901921778, (50, 2117): 675.9238352847483, (50, 2123): 741.553074247087, (50, 2124): 743.9618444517808, (50, 2134): 731.1738451024651, (50, 2138): 740.6380742839495, (50, 2141): 733.8293905295709, (50, 2148): 714.8192861918686, (50, 2150): 726.8842574199659, (50, 2151): 727.722718843059, (50, 2152): 723.9899988892564, (50, 2153): 717.7638072688259, (50, 2154): 709.0442565283303, (50, 2155): 704.0931016537202, (50, 2156): 704.9331581644009, (50, 2157): 693.7863436461541, (50, 2160): 733.1270141484464, (50, 2161): 721.2938213415428, (50, 2162): 709.8247221415241, (50, 2163): 707.0973177635241, (50, 2164): 705.5289129291818, (50, 2168): 716.1307359207296, (50, 2172): 708.0980691841366, (50, 2174): 724.5495612990553, (50, 2178): 707.1206094063265, (50, 2179): 704.6956334550307, (50, 2183): 737.8328910104865, (50, 2185): 736.5792574842568, (50, 2186): 735.3922383731701, (50, 2190): 736.0621972621972, (50, 2192): 733.409624641927, (50, 2193): 739.2990464702143, (50, 2194): 736.6200612702273, (50, 2195): 733.2048631509956, (50, 2197): 732.5271782589939, (50, 2205): 724.5028334476775, (50, 2207): 715.010478728614, (50, 2208): 719.7227539981419, (50, 2212): 746.727450888953, (50, 2214): 639.058411532745, (50, 2225): 637.3719713733365, (50, 2231): 692.0218281197896, (50, 2278): 648.8619189484943, (50, 2284): 650.8622351347746, (50, 2285): 648.136419080767, (50, 2291): 623.105278239744, (50, 2292): 639.1489509561778, (50, 2307): 646.2581269139504, (50, 2313): 617.0748550302843, (50, 2317): 640.5208393415403, (50, 2319): 639.8986747110587, (50, 2321): 640.4372576702857, (50, 2323): 644.1791638214473, (50, 2326): 663.1500641919224, (50, 2327): 660.3816706799438, (50, 2329): 658.0684657684355, (50, 2330): 654.4520834860373, (50, 2332): 657.0642472627806, (50, 2344): 656.0493514753625, (50, 2346): 652.9806867089753, (50, 2361): 677.0302877723223, (50, 2368): 694.5847707224253, (50, 2374): 695.5041047252461, (50, 2375): 697.9556527999431, (50, 2377): 689.3478849017686, (50, 2378): 698.7026303017107, (50, 2379): 696.1578386539023, (50, 2380): 699.220691015449, (50, 2383): 693.9268249205345, (50, 2385): 696.5665153446125, (50, 2395): 699.3238165334587, (50, 2397): 693.6062475507755, (50, 2398): 686.3355622436169, (50, 2399): 691.4056542166525, (50, 2400): 690.6307680887503, (50, 2402): 688.5649379846761, (50, 2403): 690.7278699943462, (50, 2404): 692.4447167835608, (50, 2405): 686.2028823557489, (50, 2407): 692.9709149678973, (50, 2408): 694.3075078917457, (50, 2409): 688.5369791417208, (50, 2411): 686.0357264052246, (50, 2412): 687.2114026611073, (50, 2413): 688.3641702733671, (50, 2414): 684.814037112417, (50, 2422): 683.7459904672986, (50, 2424): 688.8533915778665, (50, 2426): 690.2790334765946, (50, 2433): 684.352604022611, (50, 2436): 680.1863542873642, (50, 2437): 668.367846457194, (50, 2440): 671.7934340699061, (50, 2445): 708.554297739585, (50, 2447): 702.9163825565961, (50, 2454): 710.4409933911213, (50, 2455): 712.8009575536787, (50, 2460): 687.0430218231186, (50, 2461): 689.7566451021551, (50, 2471): 727.0488336407219, (50, 2492): 610.7250766015102, (50, 2511): 593.3385361936673, (50, 2523): 601.7243543292058, (50, 2525): 594.5946770054557, (50, 2535): 634.362766801009, (50, 2537): 627.6248935783713, (50, 2538): 634.0336923688004, (50, 2539): 623.8098885363794, (50, 2540): 637.2030774979721, (50, 2542): 639.1160288735941, (50, 2559): 741.055394386535, (50, 2575): 723.7999034999143, (50, 2599): 625.5800682205455, (50, 2600): 645.0304116278253, (50, 2607): 641.5784953945933, (50, 2627): 586.016665684992, (50, 2647): 598.9241873195793, (50, 2674): 596.5044260254091, (50, 2681): 591.0825069089071, (50, 2683): 600.6128117530033, (50, 2686): 592.7930176217005, (50, 2689): 700.8108349902383, (50, 2690): 700.7837001895601, (50, 2713): 709.4200914640979, (50, 2714): 710.0737068220072, (50, 2715): 713.0276384528007, (50, 2739): 710.7829962601774, (50, 2740): 696.2967143530096, (50, 2741): 698.0816306396989, (50, 2749): 705.4061765205468, (50, 2750): 706.7535213801797, (50, 2752): 709.056547703414, (50, 2755): 711.1193771701943, (50, 2758): 710.0844159624546, (50, 2759): 710.2821870834294, (50, 2769): 707.3424871605398, (50, 2771): 699.8759687077226, (50, 2779): 697.1832335557956, (50, 2784): 662.6636224814694, (50, 2800): 666.0170493810117, (50, 2802): 688.4675071574103, (50, 2803): 687.8405985580913, (50, 2804): 686.0816393403401, (50, 2805): 689.544422473383, (50, 2807): 689.8154028686563, (50, 2809): 687.7250485037932, (50, 2812): 670.0522803120848, (50, 2814): 684.1371709810019, (50, 2817): 682.1593647436449, (50, 2819): 691.3616677704383, (50, 2823): 668.2293244305436, (50, 2832): 692.5743783030265, (50, 2836): 679.4079626535147, (50, 2839): 690.2465795525341, (50, 2841): 684.0229794008281, (50, 2843): 683.5236067307421, (50, 2846): 680.3476879420637, (50, 2849): 693.9293458516935, (50, 2852): 691.1966409574453, (50, 2853): 695.1654764576397, (50, 2876): 694.779584286246, (50, 2877): 705.1818899433769, (50, 2885): 705.8902401822284, (50, 2918): 696.2232251177759, (50, 2921): 700.0568039530057, (50, 2925): 684.4405314203528, (50, 2926): 680.8880666911369, (50, 2930): 686.5324279790062, (50, 2931): 684.5560126027144, (50, 2938): 695.3167848498739, (50, 2940): 713.1267767444268, (50, 2947): 699.3377488852357, (50, 2949): 688.5752224142335, (50, 2950): 689.6250534921801, (50, 2952): 687.3821775263109, (50, 2958): 687.3449809890549, (50, 2959): 690.6154807537906, (50, 2960): 695.1539468307352, (50, 2961): 692.3424275798519, (50, 2963): 684.915128227795, (50, 2968): 685.7691228576064, (50, 2976): 684.9086905075309, (50, 2981): 636.229885341019, (50, 2982): 634.104422409056, (50, 2984): 631.6799918746509, (50, 3003): 626.8467309420324, (50, 3046): 611.1081406268253, (50, 3050): 626.4731331695805, (50, 3051): 628.6549854437358, (50, 3053): 623.3073883788543, (50, 3069): 648.7880076258057, (50, 3071): 624.9060416875765, (50, 3080): 705.3307998407496, (50, 3199): 615.6686103365738, (50, 3200): 610.1145588919993, (50, 3205): 642.7553989583291, (50, 3209): 612.813454883469, (50, 3215): 610.6815737008893, (50, 3217): 604.1443514013355, (50, 3249): 611.5492877078835, (50, 3263): 661.0574219861136, (50, 3289): 627.9827440805057, (50, 3301): 628.7810014769032, (50, 3302): 626.695278406772, (50, 3307): 623.8390705367717, (50, 3310): 631.5954771974882, (50, 3391): 644.3620280596085, (50, 3509): 445.0645664527918, (50, 3510): 449.46281946875547, (50, 3511): 447.82759249364324, (50, 3512): 451.6927866647453, (50, 3514): 451.83947735709376, (50, 3519): 428.73577431762976, (50, 3536): 439.66948908540155, (50, 3545): 434.25234100622646, (50, 3548): 442.7607898856813, (50, 3572): 435.5522037778442, (50, 3581): 436.6519524894225, (50, 3583): 444.8711822866898, (50, 3601): 418.6098159104035, (50, 3656): 421.8888424142195, (50, 3669): 424.05097119653965, (50, 3670): 419.70368813777475, (50, 3695): 445.59269522565177, (50, 3696): 442.4611148971176, (50, 3782): 470.71696125442526, (50, 3792): 470.14013787030046, (50, 3989): 2368.767031082381, (50, 4008): 2391.419717651172, (50, 4031): 2385.711344396443, (50, 4045): 2381.7078245033654, (50, 4144): 2386.8860402378555, (50, 4145): 2368.3815946691875, (50, 4164): 2379.1366892550127, (50, 4168): 2374.053655294712, (50, 4173): 2373.598061175165, (50, 4181): 2359.760918055598, (50, 4228): 2342.2079666967356, (50, 4248): 2342.5836478122774, (50, 4254): 2236.358707266539, (50, 4260): 2234.9969620876636, (50, 4262): 2244.167856599635, (50, 4273): 2241.260666712659, (50, 4319): 2174.7515473630383, (50, 4326): 2171.8757097744424, (50, 4328): 2172.401494254175, (50, 4334): 2178.4035813560804, (50, 4335): 2176.8987099051783, (50, 4372): 2163.9934354686798, (50, 4413): 2240.4725288087484, (50, 4434): 2161.0163592477033, (50, 4447): 2172.007511329052, (50, 4452): 2161.970152364273, (50, 4463): 1997.665561515135, (50, 4465): 2003.4111021512315, (50, 4619): 2246.274591127838, (50, 4645): 2264.1705284268915, (50, 4657): 2260.9791341986447, (50, 4666): 2253.8225971213274, (50, 4676): 2265.9637493721048, (50, 4678): 2268.892106918709, (50, 4689): 2260.0642685865478, (50, 4704): 2320.2447301347333, (50, 4726): 2452.99861190978, (50, 4727): 2450.496089168129, (50, 4730): 2445.6970518736653, (50, 4731): 2446.714606948368, (50, 4734): 2451.501431991471, (50, 4735): 2448.8220390376778, (50, 4736): 2449.750720705192, (50, 4737): 2445.178030982408, (50, 4738): 2445.5231473629096, (50, 4756): 2447.8611987928402, (50, 4760): 2436.817006006043, (50, 4761): 2438.84301940979, (50, 4762): 2433.023669973456, (50, 4765): 2437.867332651761, (50, 4773): 2458.228744981577, (50, 4774): 2455.4261019258465, (50, 4790): 2456.650898794357, (50, 4795): 2454.607177349571, (50, 4799): 2456.2063175113717, (50, 4801): 2460.667185589972, (50, 4804): 2456.1692358720256, (50, 4805): 2454.4813157627887, (50, 4806): 2453.6348314213246, (50, 4815): 2450.733863857083, (50, 4816): 2457.263777272843, (50, 4817): 2457.8453600173816, (50, 4826): 2454.313960662567, (50, 4830): 2450.4770221539884, (50, 4839): 2444.0763620926436, (50, 4840): 2446.0333231307654, (50, 4841): 2440.5344592475944, (50, 4846): 2438.9086214166764, (50, 4848): 2437.7830820851073, (50, 4850): 2439.962403425939, (50, 4871): 2413.467118308083, (50, 4883): 2434.805457292775, (50, 4900): 2424.607321941826, (50, 4901): 2421.053705436822, (50, 4917): 2234.402576981057, (50, 4931): 2215.4418725854257, (50, 4944): 2236.9865110915507, (50, 4956): 2218.484485336114, (50, 4958): 2217.075993071718, (50, 4959): 2212.8867140810025, (50, 4961): 2222.6750841550247, (50, 4966): 2213.3520553378403, (50, 5207): 2192.252996341671, (50, 5272): 1856.6905999643147, (50, 5283): 1863.3411197271407, (50, 5287): 1872.0611680297154, (50, 5289): 1874.9084287451378, (50, 5293): 1859.769521704074, (50, 5295): 1878.6505360226454, (50, 5296): 1877.3575146539245, (50, 5298): 1876.488079835767, (50, 5303): 1881.0756183005024, (50, 5305): 1850.5461560348358, (50, 5306): 1843.6714770979918, (50, 5307): 1846.9531541798606, (50, 5308): 1853.2670017936966, (50, 5313): 1854.4385310521038, (50, 5314): 1859.1232877309697, (50, 5317): 1852.556339843827, (50, 5319): 1874.2950964753613, (50, 5324): 1871.370235077373, (50, 5326): 1869.5573350770824, (50, 5348): 1841.1158090888862, (50, 5351): 1844.489231983468, (50, 5399): 1877.0392315352544, (50, 5413): 1850.5490912980872, (50, 5422): 1881.8312485277472, (50, 5445): 1865.8870610971721, (50, 5448): 1859.4388922833289, (50, 5456): 1856.7027824586835, (50, 5467): 1862.3722097306704, (50, 5624): 1795.501253263291, (50, 5671): 2020.52222827911, (50, 5672): 2011.8157302402917, (50, 5797): 2125.240955244766, (50, 5871): 1957.3541328760753, (50, 5976): 1880.4236045915234, (50, 6118): 211.81486028745059, (50, 6248): 357.48562932018484, (50, 6345): 1460.7286380988382, (50, 6352): 1438.898363355025, (50, 6354): 1466.0738113871726, (50, 6359): 1470.3851058511832, (50, 6376): 1442.4457992376558, (50, 6378): 1463.4810178733414, (50, 6381): 1468.6016451388655, (50, 6383): 1456.093735439758, (50, 6396): 1466.2842047371107, (50, 6399): 1461.0169180087264, (50, 6408): 1439.6706292715112, (50, 6409): 1450.0010128079427, (50, 6419): 1414.828319363794, (50, 6422): 1442.555376435121, (50, 6423): 1440.7929467892895, (50, 6424): 1464.0300297355295, (50, 6439): 1459.8778650796708, (50, 6464): 1453.8620188240725, (50, 6465): 1451.611499608729, (50, 6469): 1454.2558092374466, (50, 6470): 1452.9025823485467, (50, 6472): 1477.788977110308, (50, 6480): 1473.4301444057403, (50, 6486): 1487.0972050055605, (50, 6497): 1482.494245252761, (50, 6503): 1456.0426585934297, (50, 6508): 1457.1326511472885, (50, 6509): 1461.5932473009657, (50, 6521): 1476.3752254458934, (50, 6544): 1475.2820780920606, (50, 6552): 1446.7038123713025, (50, 6553): 1443.3247021236355, (50, 6554): 1439.8816818236112, (50, 6578): 1452.299178002198, (50, 6582): 1450.2169955283207, (50, 6601): 1453.9285501069658, (50, 6609): 1480.8444665549355, (50, 6610): 1481.8804268563315, (50, 6611): 1482.3852060846032, (50, 6614): 1480.5306426152724, (50, 6615): 1481.205582857258, (50, 6616): 1484.9700994101465, (50, 6617): 1483.3301155582633, (50, 6618): 1488.6092952712138, (50, 6619): 1478.084930706894, (50, 6620): 1485.1685765922234, (50, 6621): 1482.2972130967487, (50, 6622): 1482.8858699762511, (50, 6623): 1480.3162081892494, (50, 6624): 1477.8420866998495, (50, 6625): 1477.2407321310993, (50, 6626): 1477.8872421082326, (50, 6627): 1479.7519999127062, (50, 6628): 1484.7089975270092, (50, 6629): 1478.7924950140193, (50, 6630): 1474.601065765967, (50, 6632): 1478.4272450410472, (50, 6634): 1471.5215716427704, (50, 6635): 1481.1844969838194, (50, 6636): 1485.1749652881024, (50, 6637): 1474.8237343840212, (50, 6638): 1475.037777655278, (50, 6639): 1480.0943831431653, (50, 6640): 1475.4804254422306, (50, 6641): 1482.33213131967, (50, 6642): 1475.17013407075, (50, 6643): 1477.5058720232778, (50, 6645): 1478.5307772307665, (50, 6646): 1487.4619743545024, (50, 6647): 1476.0074764541714, (50, 6653): 1481.0476459943318, (50, 6655): 1480.1032378183015, (50, 6658): 1471.3416520281244, (50, 6662): 1475.07930246981, (50, 6819): 1311.5696957596676, (50, 6996): 1374.0109092110768, (50, 7059): 1412.6584703954484, (50, 7187): 1371.5707959885071, (50, 7304): 1273.025927904302, (50, 7528): 1379.7330820645536, (50, 7720): 1601.7866381844685, (50, 7793): 1600.3276773937755, (50, 7807): 1602.3768877158593, (50, 7808): 1599.9896106634258, (50, 7831): 1503.1119554477202, (50, 7850): 1539.0910049591728, (50, 7852): 1530.4193105977733, (50, 8012): 1586.8369415975662, (50, 8125): 1644.2616126208845, (50, 8208): 1673.3433940558868, (50, 8392): 1536.6061063268721, (50, 8651): 1125.5444056858216, (50, 9088): 1295.8547108196296, (50, 9443): 1074.6599061897214, (50, 9444): 1080.962041242841, (50, 9828): 944.8932041167493, (50, 9868): 906.6827421229066, (50, 10180): 1649.9773255403716, (50, 10256): 1750.6478563933156, (50, 10276): 1700.8417576228685, (50, 10378): 1703.1823947245773, (50, 10676): 1635.7938610115107, (50, 10714): 1576.8297964485232, (50, 10730): 1573.3533332263476, (50, 10862): 1679.2223233087618, (50, 10881): 1694.7387121871516, (50, 10883): 1693.1503934594805, (50, 10885): 1675.8521665004498, (50, 10891): 1690.7143646416635, (50, 10909): 1689.0358674988074, (50, 10911): 1690.8935495577352, (50, 10913): 1687.414317210338, (50, 10915): 1687.0897401102943, (50, 10919): 1689.1137428476368, (50, 11037): 1589.6767229164534, (50, 11039): 1548.2781593698915, (50, 11516): 2568.909441963621, (50, 11856): 2180.781398806826, (50, 11857): 2178.7255604802494, (50, 11861): 2179.9207525664347, (50, 11881): 2173.8351217627746, (50, 11902): 2156.954105290718, (50, 11911): 2152.3961110974356, (50, 11914): 2155.397201947815, (50, 11922): 2168.462646476913, (50, 11924): 2172.0561091868826, (50, 11926): 2167.1046540864463, (50, 11950): 2175.0460666998324, (50, 11963): 2191.1706607810265, (50, 11983): 2177.531491037143, (50, 11985): 2199.4002100104576, (50, 12009): 2193.8650280920074, (50, 12010): 2183.0317683263897, (50, 12018): 2184.5874011136625, (50, 12020): 2188.0362103918173, (50, 12021): 2189.661689535977, (50, 12024): 2200.572317381746, (50, 12025): 2197.3771552909916, (50, 12027): 2194.67183988245, (50, 12031): 2181.1362625546835, (50, 12032): 2185.3143037606355, (50, 12035): 2192.5791482813966, (50, 12041): 2202.175023409914, (50, 12045): 2048.231268975539, (50, 12145): 2115.4592346959, (50, 12275): 2370.443146799339, (50, 12294): 2338.1684304644295, (50, 12358): 2425.669701148502, (50, 12463): 2457.703930970602, (50, 12465): 2456.487600688845, (50, 12482): 2474.411570022315, (50, 12503): 2471.6355761516265, (50, 12506): 2475.8869367880743, (50, 12549): 2469.669053358721, (50, 12559): 2465.828952264045, (50, 12569): 2468.2556562595382, (50, 12572): 2471.513803988207, (50, 12574): 2465.034200184664, (50, 12576): 2473.72658238346, (50, 12591): 2474.6787260893625, (50, 12608): 2501.8340192962382, (50, 12696): 2461.474191103044, (50, 12710): 2488.0194110035204, (50, 12728): 2473.7397685433366, (50, 12766): 1785.5927158435024, (50, 12771): 1760.8424139498675, (50, 12790): 1756.5162143641192, (50, 12795): 1745.8233531095925, (50, 12797): 1710.361828660639, (50, 12798): 1715.9655314365123, (50, 12811): 1746.7659777961342, (50, 12830): 1735.2710484319357, (50, 12848): 1743.022260227591, (50, 12850): 1747.0652359495032, (50, 12852): 1734.5090555156225, (50, 12854): 1729.7589193374317, (50, 12859): 1748.3749493770567, (50, 12861): 1721.7536356993742, (50, 12865): 1751.5667653931407, (50, 12866): 1749.8099584003216, (50, 12867): 1758.7131430435745, (50, 12874): 1754.2972741112083, (50, 12875): 1758.1888068288415, (50, 12881): 1742.64976946468, (50, 12883): 1748.6096530765162, (50, 12885): 1761.1547919867733, (50, 12888): 1746.3367587487148, (50, 12889): 1745.4592892733049, (50, 12892): 1755.0540296169443, (50, 12893): 1746.081284341545, (50, 12896): 1749.394470649415, (50, 12906): 1752.552326839664, (50, 13018): 1698.6310787224731, (50, 13071): 1696.9463519367055, (50, 13131): 1667.6427297864345, (50, 13146): 1701.3133401866228, (50, 13159): 1645.7676316398404, (50, 13193): 1662.2217211402794, (50, 13198): 1610.9842776992743, (50, 13292): 1675.9226305705565, (50, 13296): 1698.8165702811539, (50, 13406): 1569.5470764058653, (50, 13407): 1567.2182963076557, (50, 13417): 1559.220823240178, (50, 13418): 1564.6668342767675, (50, 13438): 1592.0204311391678, (50, 13442): 1598.1511550752366, (50, 13443): 1593.2798273575238, (50, 13764): 1167.2201435397528, (50, 13766): 1173.3482578819344, (50, 13771): 1167.5857462518604, (50, 13783): 1161.895313833115, (50, 13784): 1179.9647531474457, (50, 13792): 1156.2701933541905, (50, 13824): 1157.6983124860424, (50, 14017): 1194.7964938483992, (50, 14870): 1673.1868100101317, (50, 14997): 1346.0539372926296, (50, 15000): 1348.5222559884114, (50, 15003): 1354.4931396704478, (50, 15006): 1355.4605839041824, (50, 15007): 1359.7782104156818, (50, 15056): 1364.7514133177306, (50, 15063): 1362.1733824631283, (50, 15069): 1362.960666587101, (50, 15076): 1361.71439648398, (50, 15086): 1346.431097159733, (50, 15087): 1344.507281943693, (50, 15111): 1330.2909819189094, (50, 15116): 1338.637445556707, (50, 15722): 1227.8748320666652, (50, 15998): 1210.6502331327458, (50, 16073): 454.6691260017938, (50, 16939): 432.02052685858746, (50, 16940): 429.3793147628922, (50, 16951): 423.6056047259466, (50, 16963): 426.0278089786126, (50, 16965): 433.2593401684369, (50, 16969): 426.98432749442446, (50, 16970): 430.3397314176567, (50, 16971): 424.1709116728152, (50, 16973): 420.5977663624881, (50, 16974): 433.1933565608952, (50, 16976): 432.8165367926577, (50, 16978): 429.42743710749556, (50, 16980): 437.7925415650268, (50, 16982): 429.921533413497, (50, 17045): 500.41033555036637, (50, 17048): 508.93869986518916, (50, 17304): 2314.635861542175, (50, 17305): 2308.200741354359, (50, 17330): 2312.826211767998, (50, 17334): 2307.0778075588537, (50, 17343): 2318.3365935701504, (50, 17345): 2304.3304689817664, (50, 17347): 2310.672642563334, (50, 17351): 2296.248031146605, (50, 17372): 2305.260365457416, (50, 17373): 2318.242177914984, (50, 17377): 2318.9530275507564, (50, 17382): 2309.9799357043303, (50, 17383): 2312.46998923454, (50, 17389): 2306.9753405054325, (50, 17400): 2316.512381147818, (50, 17401): 2316.72222767608, (50, 17402): 2316.8067922764767, (50, 17403): 2317.502888475487, (50, 17440): 2302.213351908928, (50, 17455): 2315.14556361745, (50, 17491): 2314.1849567858167, (50, 17507): 2307.332238858426, (50, 17509): 2313.0431410643273, (50, 17590): 2290.0994545416524, (50, 17615): 2277.578349141837, (50, 17642): 2281.456519500731, (50, 17643): 2280.0697464037494, (50, 17668): 2277.9635821108177, (50, 17721): 2271.2562614845856, (50, 17754): 2320.9548745154807, (50, 17769): 2311.8068803383812, (50, 17776): 2287.010863609656, (50, 17804): 2320.54740769235, (50, 17809): 2325.6917211605796, (50, 17824): 2323.884389380774, (50, 17837): 2301.7084755083993, (50, 17838): 2300.8749810194754, (50, 17862): 2296.3860181793457, (50, 17866): 2307.989428893276, (50, 17872): 2293.5418566913017, (50, 17873): 2284.36463682302, (50, 17881): 2298.238387936047, (50, 17947): 572.906806635334, (50, 17951): 570.2132345693085, (50, 17953): 573.4392170281332, (50, 17954): 576.0440113025177, (50, 17959): 565.9085754634718, (50, 17963): 558.5109304818033, (50, 18000): 559.8529601904684, (50, 18001): 564.7131167260923, (50, 18111): 763.2400951901942, (50, 18148): 760.5669863219323, (50, 18166): 767.239511569906, (50, 18189): 747.923602711987, (50, 18239): 2321.782847606426, (50, 18240): 2321.415055004594, (50, 18245): 2322.104832970883, (50, 18247): 2320.6532295944016, (50, 18251): 2321.71225402864, (50, 18256): 2322.5027628192183, (50, 18258): 2321.0353937517784, (50, 18259): 2321.1024019026677, (50, 18260): 2321.371954485877, (50, 18262): 2322.110676371027, (50, 18263): 2322.6663722388203, (50, 18264): 2322.9541519523486, (50, 18266): 2322.2195287436625, (50, 18267): 2322.5444120961147, (50, 18268): 2322.58930576661, (50, 18269): 2323.2040402540806, (50, 18275): 2322.912623443048, (50, 18285): 2322.977416771992, (50, 18308): 2316.4852628700605, (50, 18313): 2313.420248500644, (50, 18314): 2313.8632563165825, (50, 18315): 2324.0228377215, (50, 18316): 2323.54972465287, (50, 18317): 2323.81132288978, (50, 18320): 2324.654382693547, (50, 18321): 2324.612234879371, (50, 18322): 2325.1082947391888, (50, 18324): 2326.100297398458, (50, 18325): 2328.2157405991, (50, 18326): 2327.4465306028715, (50, 18327): 2323.706261093849, (50, 18329): 2329.6257736357993, (50, 18330): 2327.286953857601, (50, 18331): 2326.073684838847, (50, 18332): 2324.611390417646, (50, 18333): 2327.4327030051068, (50, 18336): 2326.8612993313727, (50, 18337): 2327.842741424776, (50, 18403): 2324.4565904512497, (50, 18432): 2283.601766184239, (50, 18451): 2311.2302627522827, (50, 18466): 2339.227963785586, (50, 18481): 2325.6606395552376, (50, 18483): 2325.371277964932, (50, 18484): 2324.428430968113, (50, 18485): 2321.881005835248, (50, 18486): 2326.0249733774485, (50, 18487): 2323.6640296967216, (50, 18489): 2324.728666118046, (50, 18490): 2328.2088735997786, (50, 18491): 2329.4842830225307, (50, 18492): 2320.6998389558566, (50, 18493): 2325.9128296902145, (50, 18494): 2323.9782754401876, (50, 18495): 2327.301425364326, (50, 18496): 2325.729789257034, (50, 18497): 2323.3844237864582, (50, 18498): 2322.8430510909407, (50, 18499): 2324.7215825332178, (50, 18501): 2323.8670714861205, (50, 18502): 2322.697864147237, (50, 18503): 2321.45292090937, (50, 18504): 2325.9046573104297, (50, 18506): 2324.8668868451027, (50, 18507): 2323.9137734072824, (50, 18508): 2324.737279942297, (50, 18509): 2325.032299683968, (50, 18510): 2321.882629295721, (50, 18511): 2326.8576480045435, (50, 18512): 2324.8937961267825, (50, 18515): 2326.4247548143826, (50, 18516): 2327.4576637369637, (50, 18517): 2326.38824596299, (50, 18518): 2328.202631236196, (50, 18519): 2326.000426205443, (50, 18520): 2324.0397502116602, (50, 18522): 2330.5855868138638, (50, 18523): 2331.1657651379555, (50, 18532): 2333.31738626319, (50, 18535): 2329.166736345448, (50, 18537): 2326.855927099872, (50, 18539): 2327.501248617762, (50, 18540): 2327.9415613567353, (50, 18541): 2329.2205523914313, (50, 18542): 2330.003060107274, (50, 18543): 2326.242507883471, (50, 18546): 2328.5546552655314, (50, 18555): 2332.205712603006, (50, 18556): 2333.080430600519, (50, 18565): 2333.4650040132897, (50, 18567): 2335.137171983101, (50, 18568): 2332.8876097153307, (50, 18577): 2347.035993013581, (50, 18583): 2343.8152661743998, (50, 18605): 2345.7725227317683, (50, 18608): 2337.5849487409705, (50, 18616): 2359.0458212800804, (50, 18618): 2370.8778236307726, (50, 18625): 2364.7775393641277, (50, 18645): 2353.886974774899, (50, 18646): 2357.2263404195533, (50, 18653): 2349.9553130696895, (50, 18654): 2359.1232626410288, (50, 18655): 2353.5569404081416, (50, 18666): 2386.460904469788, (50, 18837): 2313.2727083229192, (50, 18974): 2303.9169159683943, (50, 18999): 2309.6034235484894, (50, 19000): 2312.9238923998205, (50, 19174): 2136.509698204186, (50, 19342): 2198.3714224746436, (50, 19455): 2174.512272039044, (50, 19555): 2003.5236982788326, (50, 19564): 2007.4923419300385, (50, 19573): 2001.675223742205, (50, 19586): 1999.4559317919102, (50, 19605): 2003.0141346802982, (50, 19611): 2007.1590719601043, (50, 19614): 2006.8509201759523, (50, 19641): 2083.2722663247705, (50, 19702): 2080.1525919684027, (50, 19713): 2074.9187917940503, (50, 19731): 1985.2997454622305, (50, 19819): 2145.623498763749, (50, 19893): 2043.3164035418995, (50, 19899): 2082.5907822032773, (50, 19929): 2053.0602838284876, (50, 19951): 2129.2074171997065, (50, 19962): 2060.362752728993, (50, 19970): 2074.918071817971, (50, 19971): 2075.768911190756, (50, 19972): 2069.720080546894, (50, 19975): 2066.3493014386663, (50, 19978): 2143.2580390607013, (50, 19987): 2144.275939594316, (50, 19989): 2123.326504247911, (50, 20039): 2147.989404656799, (50, 20043): 2156.3512767021352, (50, 20047): 2149.3063328265703, (50, 20052): 2126.447055964368, (50, 20054): 2128.45889626805, (50, 20085): 2231.002920685018, (50, 20104): 2237.4851577312847, (50, 20132): 2198.158337703699, (50, 20203): 2043.6556879863476, (50, 20280): 2036.443583375866, (50, 20285): 2034.8395295006158, (50, 20290): 2039.8423263752452, (50, 20297): 2032.6372780969728, (50, 20309): 2151.6317107745513, (50, 20453): 2257.625222574032, (50, 20485): 1987.4444525416625, (50, 20520): 1969.1223174257834, (50, 20526): 1963.7775012087056, (50, 20698): 1014.1118145521164, (50, 20868): 818.2467638627127, (50, 21042): 1777.7098536494793, (50, 21057): 1819.318035420877, (50, 21066): 1800.369854257429, (50, 21075): 1790.4462086508358, (50, 21093): 1782.8912197043692, (50, 21098): 1815.4241099878147, (50, 21127): 1782.2212458723436, (50, 21130): 1791.0770182413016, (50, 21144): 1787.9677233036668, (50, 21146): 1779.4916058149818, (50, 21147): 1786.6977305452094, (50, 21148): 1794.60426362883, (50, 21153): 1769.9982100244172, (50, 21293): 1849.367761490609, (50, 21426): 1821.3024473309074, (50, 21442): 1862.9919811041796, (50, 21451): 1867.0960519591501, (50, 21466): 1842.8823981205765, (50, 21469): 1849.8648805701346, (50, 21471): 1839.3054161513578, (50, 21473): 1845.2785884404323, (50, 21475): 1840.1579354213966, (50, 21482): 1853.6060596788993, (50, 21484): 1852.5048715987323, (50, 21488): 1848.2285942549772, (50, 21494): 1841.0507771603784, (50, 21498): 1846.0152192455648, (50, 21500): 1838.9013965636125, (50, 21514): 1856.0490827484646, (50, 21537): 1839.568336927052, (50, 21662): 1864.6349087296514, (50, 21691): 1838.0874483457112, (50, 21757): 1783.5575052262543, (50, 21777): 1703.9515104646596, (50, 21778): 1697.3101885708606, (50, 21779): 1702.023102080306, (50, 21790): 1710.354478620459, (50, 21802): 1711.9527799625278, (50, 21824): 1719.8480969673192, (50, 21874): 1704.9833347672068, (50, 21879): 1702.9397173545365, (50, 21983): 1720.9527177317966, (50, 22002): 1799.1886154223816, (50, 22132): 1732.5493467879703, (50, 22261): 1002.3246915378284, (50, 22298): 1021.7609458497317, (50, 22339): 998.920725804889, (50, 22508): 1094.683922918367, (50, 22841): 757.384273679748, (50, 22842): 755.675056236489, (50, 22874): 735.6998742300016, (50, 22941): 743.0728203114122, (50, 22956): 750.113711671101, (50, 22960): 756.8159673059421, (50, 22968): 742.3082483629868, (50, 22970): 747.919140413649, (50, 22974): 738.5608922714989, (50, 22980): 749.11624019534, (50, 23025): 729.7627746237617, (50, 23028): 723.7481198799661, (50, 23081): 722.305127028404, (50, 23104): 678.81312766133, (50, 23147): 626.4632189685913, (50, 23298): 1977.140728591701, (50, 23376): 1958.3611666146253, (50, 23381): 1951.5094676908545, (50, 23529): 1992.6735612075872, (50, 23556): 1981.2591420459835, (50, 23718): 1962.0356591219822, (50, 24001): 2087.5919005046603, (50, 24094): 2129.76958229668, (50, 24129): 2148.4587761453918, (50, 24174): 2112.6923985159688, (50, 24235): 2156.2224992453894, (50, 24259): 2172.0589472892407, (50, 24260): 2171.026820741871, (50, 24261): 2166.725819331827, (50, 24305): 2192.5539224139125, (50, 24306): 2196.5774832031443, (50, 24307): 2190.8909169727654, (50, 24308): 2129.21365093631, (50, 24498): 2233.7001414085034, (50, 24499): 2234.2558846075012, (50, 24500): 2230.635483568889, (50, 24668): 2199.369713525332, (50, 24711): 2260.608205307051, (50, 24756): 2276.2498294787147, (50, 24788): 2280.3217042276888, (50, 24809): 2262.6118532819155, (50, 24813): 2267.8548408643, (50, 24821): 2266.0015149455753, (50, 24825): 2267.938664691518, (50, 24832): 2260.96180531117, (50, 24833): 2263.9862407613227, (50, 24835): 2267.170914877239, (50, 24837): 2271.580719407863, (50, 24840): 2260.7019195399266, (50, 24841): 2264.9438038999533, (50, 24844): 2261.122265345287, (50, 24845): 2262.773993246361, (50, 24846): 2264.0653840897958, (50, 24849): 2265.849273327727, (50, 24850): 2269.1227273559152, (50, 24863): 2225.025870912038, (50, 24866): 2230.3225661157985, (50, 24885): 2237.672679823405, (50, 24886): 2238.757645478946, (50, 24889): 2248.367838419282, (50, 24903): 2251.96940974835, (50, 24909): 2230.782214299879, (50, 24999): 2457.220498803376, (50, 25019): 2448.5641847137003, (50, 25028): 2454.580420202011, (50, 25137): 2057.3947466678733, (50, 25145): 2064.685218138815, (50, 25208): 2155.339348678777, (50, 25233): 2145.656039077716, (50, 25371): 2053.389832173317, (50, 25377): 2031.1459189679772, (50, 25828): 1651.8543487371403, (50, 25851): 1589.697596875061, (50, 25874): 1645.6987113837345, (50, 25898): 1675.0473072389323, (50, 25946): 1645.7019555754932, (50, 26047): 1774.7086138685625, (50, 26066): 1889.5986672555136, (50, 26197): 1811.6183924936133, (50, 26212): 1489.522293178343, (50, 26253): 1473.8608609727517, (50, 26254): 1478.96493684873, (50, 26257): 1487.1742821754033, (50, 26258): 1477.796203872171, (50, 26260): 1482.4114364642805, (50, 26266): 1470.176034784076, (50, 26267): 1476.6287146033753, (50, 26271): 1477.5861372768236, (50, 26304): 1531.2011968044412, (50, 26305): 1528.8411464350677, (50, 26363): 1639.5515710342493, (50, 26441): 1163.7534293745657, (50, 26442): 1161.7940782859423, (50, 26450): 1167.408259084498, (50, 26459): 1180.1774861888275, (50, 26462): 1184.8857856056327, (50, 26467): 1171.2298002966625, (50, 26471): 1168.6480864435182, (50, 26472): 1167.2006489718542, (50, 26473): 1165.568167828449, (50, 26476): 1149.433408241332, (50, 26485): 1171.6117437360301, (50, 26493): 1165.0908976429623, (50, 26524): 1188.3401501004373, (50, 26525): 1185.4835781822037, (50, 26556): 1171.106220174259, (50, 26560): 1182.005335438927, (50, 26561): 1187.3658783086933, (50, 26564): 1169.533169177184, (50, 26569): 1184.6517818485668, (50, 26570): 1181.8786163450707, (50, 26573): 1175.5710083862982, (50, 26581): 1170.7575630644958, (50, 26583): 1174.859920823378, (50, 26593): 1164.4981793702495, (50, 26837): 1165.2296390046488, (50, 26844): 1164.5420353749662, (50, 26863): 1153.9509600453882, (50, 26893): 1146.6914549613236, (50, 26902): 1145.329595356896, (50, 26905): 1157.7143889468907, (50, 26912): 1153.1856484125506, (50, 26921): 1151.1881451333381, (50, 26922): 1137.2243914260578, (50, 27212): 1412.0382102895394, (50, 27218): 1423.5523039673153, (50, 27239): 1408.8832135972675, (50, 27257): 1405.415086990734, (50, 27274): 1406.5292005566357, (50, 27279): 1402.3136064186176, (50, 27282): 1403.0520357720213, (50, 27283): 1411.0577817904118, (50, 27285): 1403.6514742440743, (50, 27286): 1396.8237619794709, (50, 27290): 1403.0184544054969, (50, 27295): 1409.8607306218723, (50, 27300): 1408.1029414486547, (50, 27344): 1390.8851522025768, (50, 27366): 1385.7578665460615, (50, 27383): 1394.5929323602627, (50, 27398): 1404.2775919131243, (50, 27406): 1408.040966538477, (50, 27407): 1411.293094511979, (50, 27426): 1441.0851373057308, (50, 27432): 1435.1735665259582, (50, 27460): 1442.667388151356, (50, 27523): 1318.659578020635, (50, 27545): 1387.1284411308336, (50, 27602): 1362.4103065318427, (50, 27606): 1368.2742119972827, (50, 27646): 1282.9401069987264, (50, 27667): 1277.5113133216876, (50, 27672): 1280.6613493445461, (50, 27674): 1279.3967873262734, (50, 27688): 1292.114842839851, (50, 27692): 1275.9128049539406, (50, 27693): 1275.9309838357242, (50, 27705): 1272.088964504799, (50, 27712): 1268.7921174689661, (50, 27786): 1501.1963472923487, (50, 27790): 1545.9980138466751, (50, 27791): 1552.5533639940545, (50, 27795): 1496.2361968874234, (50, 27801): 1525.4532608591462, (50, 27813): 1496.333102378544, (50, 27816): 1505.0877876056454, (50, 27823): 1526.976028111531, (50, 27830): 1515.1359702541185, (50, 27884): 1255.5893724093319, (50, 27885): 1279.5242884791592, (50, 27896): 1266.7677492370783, (50, 27919): 1269.5242124626939, (50, 27922): 1267.0733980270843, (50, 27930): 1263.7381422655071, (50, 27934): 1261.3768067597734, (50, 27935): 1258.3146691250422, (50, 27948): 1180.9916316622546, (50, 27951): 1240.7336631751434, (50, 28061): 787.1457171376106, (50, 28290): 822.2033355084895, (50, 28292): 806.4472677303485, (50, 28293): 817.7364772816604, (50, 28295): 805.8800771816348, (50, 28296): 816.1702642110486, (50, 28297): 829.350371848421, (50, 28302): 818.7345126307017, (50, 28310): 9.511630147851157, (50, 28313): 30.734924400669982, (50, 28372): 11.913453795859267, (50, 28398): 9.742738934634605, (50, 28399): 5.968571752855477, (50, 28400): 8.758100076001078, (50, 28401): 11.764830127719451, (50, 28445): 42.82302253221329, (50, 28475): 43.49098178134568, (50, 28885): 2162.963325964529, (50, 28886): 2159.6027845979797, (50, 28915): 2163.5658799865937, (50, 28916): 2160.2590018214064, (50, 28917): 2158.5089371877298, (50, 28921): 2169.4325240887815, (50, 28931): 2168.6949510498853, (50, 28945): 2153.9352734703607, (50, 28982): 2157.279280310025, (50, 29219): 2182.4358998906937, (50, 29228): 2166.120761874661, (50, 29246): 2274.245439510894, (50, 29248): 2273.652284069802, (50, 29282): 2251.3802255971873, (50, 29290): 2284.1556677397607, (50, 29291): 2279.975638418031, (50, 29292): 2284.0161068895595, (50, 29293): 2275.354268627737, (50, 29294): 2282.617463750115, (50, 29298): 2276.241983000558, (50, 29299): 2275.73642655364, (50, 29304): 2267.123238356352, (50, 29317): 2246.025718092383, (50, 29323): 2244.3605981970113, (50, 29330): 2254.5665194934154, (50, 29331): 2259.437563651582, (50, 29344): 2186.1054177938167, (50, 29445): 2003.3289257084907, (50, 29724): 809.5461239617366, (50, 29738): 811.8524189279443, (50, 29745): 808.2167902354896, (50, 29748): 825.3255202581178, (50, 29750): 835.7360589334573, (50, 29759): 820.2817983064921, (50, 29772): 828.8861496112094, (50, 29781): 827.4570513656809, (50, 29784): 819.1941609766449, (50, 29790): 832.1299792811914, (50, 29811): 834.3586823463178, (50, 29817): 892.6192177360662, (50, 29818): 891.6047165823552, (50, 29929): 797.7277540450318, (50, 30039): 788.6075093799225, (50, 30066): 745.7590579164532, (50, 30116): 696.0289136566497, (50, 30238): 651.1309755522623, (50, 30248): 618.984603054732, (50, 30260): 615.4297770500742, (50, 30545): 2103.93128709653, (50, 30733): 1926.6718613443215, (50, 30756): 1889.1760821948214, (50, 30921): 1969.9554690583443, (50, 31079): 1472.4324711143634, (50, 31149): 1460.700599460941, (50, 31154): 1459.2712415368305, (50, 31160): 1459.6613462533269, (50, 31163): 1456.6499504108033, (50, 31189): 1392.0571523032036, (50, 31215): 1393.9818117360483, (50, 31259): 1376.7139848564616, (50, 31262): 1370.2018704545137, (50, 31430): 1474.2916192749824, (50, 31568): 1267.3692980580067, (50, 31751): 1431.13509323777, (53, 109): 2372.895698269785, (53, 872): 773.5991977137778, (53, 873): 766.8092683378298, (53, 877): 765.9983581735147, (53, 879): 764.6624831018511, (53, 884): 764.0973791910712, (53, 889): 761.3662208224498, (53, 891): 767.2595781855995, (53, 892): 760.0921557165697, (53, 894): 762.3282404696939, (53, 896): 774.4515260332607, (53, 903): 761.9255528435607, (53, 909): 784.4820238570641, (53, 910): 784.8732084270173, (53, 912): 788.6245105862247, (53, 913): 791.644703659094, (53, 916): 797.4349481872455, (53, 926): 786.770391767976, (53, 927): 789.7306246769541, (53, 948): 770.2863757844367, (53, 961): 779.7018967353656, (53, 962): 781.1084028062021, (53, 963): 781.9950161015082, (53, 967): 760.3992080017625, (53, 974): 756.3002173232567, (53, 998): 754.9489015529762, (53, 1014): 661.856062259097, (53, 1086): 883.4770969283927, (53, 1087): 896.2258423516437, (53, 1089): 895.5576837848429, (53, 1090): 892.0100087317101, (53, 1092): 883.2293845138678, (53, 1097): 887.5641047970375, (53, 1107): 886.5446463242943, (53, 1387): 1973.0138279641722, (53, 1554): 2065.572941609943, (53, 1827): 414.7838730238313, (53, 1828): 416.25995230650295, (53, 1829): 414.16245851828774, (53, 1830): 405.5934871687216, (53, 1831): 406.8139631608318, (53, 1832): 408.2431359948542, (53, 1833): 409.7849884263363, (53, 1836): 412.1517059419794, (53, 1841): 406.67471190899965, (53, 1843): 407.97852730454895, (53, 1844): 405.80505331060004, (53, 1845): 405.9724614872276, (53, 1847): 415.7779523686408, (53, 1848): 413.4303077536382, (53, 1849): 400.983896172209, (53, 1850): 401.3493705907024, (53, 1851): 407.39986401618097, (53, 1852): 403.56916514955964, (53, 1854): 405.35071750044386, (53, 1856): 411.26404460857594, (53, 1857): 411.58355248931053, (53, 1858): 404.60166692982796, (53, 1861): 411.11309731957476, (53, 1866): 408.25313384122296, (53, 1867): 409.7158694438863, (53, 1868): 413.7905050954238, (53, 1870): 401.18853967178507, (53, 1871): 413.0778024709874, (53, 1875): 407.9503739441147, (53, 1880): 413.12555700831416, (53, 1882): 407.2323455268724, (53, 1883): 405.507366901117, (53, 1889): 418.15182541482125, (53, 1893): 420.1250442794489, (53, 1894): 422.49759750815855, (53, 1899): 421.8620245794313, (53, 1900): 422.13342416166773, (53, 1902): 417.8616542518712, (53, 1905): 413.74749574117084, (53, 1907): 415.8324575417727, (53, 1910): 419.7660677861245, (53, 1917): 422.54588678570997, (53, 1920): 418.9592662974652, (53, 1935): 420.7149984420763, (53, 1937): 418.08365839371675, (53, 1946): 433.1667449091969, (53, 1949): 433.5350271284191, (53, 1950): 429.63995288891624, (53, 1951): 429.4566116053051, (53, 1952): 418.04199823680955, (53, 1953): 425.9842878949551, (53, 1954): 420.7634342088338, (53, 1958): 429.97366428904087, (53, 1960): 425.07361833177, (53, 1968): 423.1662325131423, (53, 1969): 427.6915906822252, (53, 1974): 425.8005173008211, (53, 1975): 423.3817812900222, (53, 1979): 431.28794705687534, (53, 1980): 424.2943835323072, (53, 1981): 427.9304578919432, (53, 1985): 429.2021209460242, (53, 1994): 415.42663684191734, (53, 2011): 404.8635347280925, (53, 2019): 382.9091198498696, (53, 2020): 385.729377671236, (53, 2029): 389.55980692968734, (53, 2030): 387.802611214154, (53, 2032): 386.6297923962913, (53, 2033): 388.0406433022725, (53, 2034): 384.56110306666, (53, 2036): 375.4170999616185, (53, 2037): 378.2454549019209, (53, 2038): 394.14268934328595, (53, 2042): 373.0688788532746, (53, 2050): 394.14667661464546, (53, 2051): 390.65331649313157, (53, 2053): 391.7497085839599, (53, 2054): 389.71738153823986, (53, 2066): 393.1985497576085, (53, 2067): 395.13011622186286, (53, 2071): 421.0185327221813, (53, 2072): 420.24059013405156, (53, 2073): 439.4180514160405, (53, 2074): 437.5525211370739, (53, 2080): 437.73680823246525, (53, 2082): 419.014068832498, (53, 2083): 418.88726137643516, (53, 2089): 425.14080386087613, (53, 2090): 425.65522786779934, (53, 2092): 429.8662147697857, (53, 2098): 440.1255459147442, (53, 2099): 435.9677350742163, (53, 2101): 437.28978573191387, (53, 2102): 432.3726530167207, (53, 2103): 432.55255271309767, (53, 2104): 431.1518565949686, (53, 2106): 416.31541393283203, (53, 2112): 433.6205896752823, (53, 2113): 429.69838827851606, (53, 2114): 422.9189756808043, (53, 2117): 412.71472688766283, (53, 2123): 552.7947482758476, (53, 2124): 552.1696530486796, (53, 2134): 545.0205888486346, (53, 2138): 546.685572623418, (53, 2141): 547.5445099213664, (53, 2148): 511.82601902563306, (53, 2150): 547.5803832641923, (53, 2151): 544.2891662367496, (53, 2152): 545.6293854499728, (53, 2153): 514.8748627240134, (53, 2154): 520.1988475489978, (53, 2155): 514.8005672848926, (53, 2156): 519.5656852772388, (53, 2157): 497.6765472496321, (53, 2160): 528.9299643970112, (53, 2161): 542.3352451777747, (53, 2162): 501.63812044480613, (53, 2163): 503.8884014285255, (53, 2164): 501.87461219698423, (53, 2168): 529.5804044655443, (53, 2172): 513.0914956902922, (53, 2174): 540.020192434729, (53, 2178): 507.8205231281222, (53, 2179): 507.04011223276734, (53, 2183): 542.678825531032, (53, 2185): 540.4762432206509, (53, 2186): 542.1426605446728, (53, 2190): 532.6303112444128, (53, 2192): 534.879331762862, (53, 2193): 543.7094294198123, (53, 2194): 545.9883988761632, (53, 2195): 541.6971731463724, (53, 2197): 532.1199966710195, (53, 2205): 528.8545821461072, (53, 2207): 526.2287649163515, (53, 2208): 526.760656982943, (53, 2212): 553.2483074445377, (53, 2214): 526.4740908290911, (53, 2225): 508.53711837263, (53, 2231): 610.4109982663173, (53, 2278): 456.01865441814016, (53, 2284): 443.88447435402423, (53, 2285): 441.7485190244776, (53, 2291): 433.7988019484499, (53, 2292): 454.8777647828963, (53, 2307): 446.670029367314, (53, 2313): 428.283884637486, (53, 2317): 467.9195981979971, (53, 2319): 450.8164098021709, (53, 2321): 444.63206325539863, (53, 2323): 451.3220647111744, (53, 2326): 454.3536319734268, (53, 2327): 456.54750231117254, (53, 2329): 457.38844038126234, (53, 2330): 456.83949687852964, (53, 2332): 450.10922448018187, (53, 2344): 465.13493231370904, (53, 2346): 460.73352736865826, (53, 2361): 499.5699049094415, (53, 2368): 453.46855098344355, (53, 2374): 447.67713973359133, (53, 2375): 449.34465991916534, (53, 2377): 460.44779481655496, (53, 2378): 445.96124473264, (53, 2379): 440.97607741865875, (53, 2380): 443.63204990696914, (53, 2383): 461.24474170824124, (53, 2385): 461.71008653857194, (53, 2395): 465.8096092700909, (53, 2397): 439.73023089958053, (53, 2398): 463.525333592369, (53, 2399): 462.7685021285675, (53, 2400): 463.52168310809583, (53, 2402): 445.63767692463597, (53, 2403): 443.48675200554294, (53, 2404): 444.8856770165017, (53, 2405): 448.33153052438115, (53, 2407): 448.3406454697481, (53, 2408): 443.8241208094866, (53, 2409): 448.01345043244953, (53, 2411): 435.6100642411086, (53, 2412): 439.1325491425172, (53, 2413): 436.282349384183, (53, 2414): 438.092672671836, (53, 2422): 433.5241520006639, (53, 2424): 440.2558791233337, (53, 2426): 441.40013350280634, (53, 2433): 442.27523179806917, (53, 2436): 438.20703669055223, (53, 2437): 452.4693325494281, (53, 2440): 450.66104902625506, (53, 2445): 355.23896059359674, (53, 2447): 365.7231972573457, (53, 2454): 360.39190659399384, (53, 2455): 364.0445750567742, (53, 2460): 376.033969123027, (53, 2461): 373.5892592092228, (53, 2471): 319.94647715457074, (53, 2492): 215.79001707083555, (53, 2511): 261.4103797964594, (53, 2523): 237.64324564991614, (53, 2525): 234.96124299863695, (53, 2535): 297.4568006506672, (53, 2537): 299.87609363160817, (53, 2538): 301.7161729187991, (53, 2539): 285.84117916127815, (53, 2540): 295.96287186778454, (53, 2542): 288.18116847669245, (53, 2559): 286.25477900142323, (53, 2575): 264.6173153228352, (53, 2599): 387.672055687163, (53, 2600): 356.45595880442363, (53, 2607): 387.87777902771603, (53, 2627): 194.70718688784558, (53, 2647): 169.61542530259524, (53, 2674): 192.2607288355544, (53, 2681): 187.4650440703171, (53, 2683): 182.8020142441489, (53, 2686): 195.14448743204983, (53, 2689): 103.5013934431349, (53, 2690): 100.76232592293094, (53, 2713): 17.481754309823437, (53, 2714): 7.492460774808134, (53, 2715): 9.221769343251237, (53, 2739): 10.420638148047976, (53, 2740): 41.71015769716123, (53, 2741): 43.120993971909165, (53, 2749): 1.1912772138358627, (53, 2750): 2.5841920694946094, (53, 2752): 4.959981610035575, (53, 2755): 5.380785596111121, (53, 2758): 4.58783644397062, (53, 2759): 4.418396822860942, (53, 2769): 4.718453104033239, (53, 2771): 32.89794478295309, (53, 2779): 10.276870779402566, (53, 2784): 43.20767378052964, (53, 2800): 48.860629749455285, (53, 2802): 32.370661742566995, (53, 2803): 35.73137549331747, (53, 2804): 38.0816395611176, (53, 2805): 23.375869050421436, (53, 2807): 25.769593666649826, (53, 2809): 22.19022734764857, (53, 2812): 43.595638624251755, (53, 2814): 23.724475566759555, (53, 2817): 46.491011439364875, (53, 2819): 31.88426674413318, (53, 2823): 37.97148312032609, (53, 2832): 17.433543397393027, (53, 2836): 30.011241065713296, (53, 2839): 28.308750859527084, (53, 2841): 32.989093476842044, (53, 2843): 29.394713911894492, (53, 2846): 25.51959720337068, (53, 2849): 12.992216700892408, (53, 2852): 16.678749695653, (53, 2853): 11.300232947579742, (53, 2876): 16.63165930572096, (53, 2877): 16.883784276944315, (53, 2885): 49.382752885028474, (53, 2918): 50.64209548897837, (53, 2921): 44.97307068062981, (53, 2925): 82.57785871618537, (53, 2926): 101.0294680431846, (53, 2930): 44.07007777096158, (53, 2931): 73.06965994265518, (53, 2938): 45.07387827212115, (53, 2940): 68.52505506204797, (53, 2947): 79.76304739550191, (53, 2949): 55.73229937846023, (53, 2950): 49.415107737127705, (53, 2952): 50.57032253608171, (53, 2958): 52.91918513848238, (53, 2959): 57.77653742938626, (53, 2960): 53.28603406589593, (53, 2961): 51.95349584207734, (53, 2963): 51.18050375330888, (53, 2968): 47.355425328831295, (53, 2976): 54.560453788426784, (53, 2981): 71.99722029572831, (53, 2982): 72.67267463303014, (53, 2984): 74.89732590781423, (53, 3003): 79.08619380010958, (53, 3046): 131.49624019270848, (53, 3050): 92.36023324315153, (53, 3051): 91.71512405397365, (53, 3053): 95.30709216749756, (53, 3069): 64.4714818478421, (53, 3071): 103.27208279204757, (53, 3080): 60.858012966238554, (53, 3199): 98.22543501574214, (53, 3200): 104.96067383691448, (53, 3205): 76.51030038896859, (53, 3209): 103.0035218339174, (53, 3215): 102.89949032548452, (53, 3217): 109.04916665193593, (53, 3249): 100.57631536514205, (53, 3263): 54.89599572512988, (53, 3289): 81.32341788846082, (53, 3301): 84.05840610313709, (53, 3302): 84.60962327889636, (53, 3307): 86.95150391398862, (53, 3310): 81.45541935200531, (53, 3391): 234.4804260986128, (53, 3509): 1124.6539580904703, (53, 3510): 1129.2917245256112, (53, 3511): 1126.5555105743638, (53, 3512): 1129.746846748613, (53, 3514): 1129.0774785069527, (53, 3519): 1112.3033532181364, (53, 3536): 1117.1101597066252, (53, 3545): 1110.2314147540637, (53, 3548): 1117.8719352074793, (53, 3572): 1114.031125604131, (53, 3581): 1118.566674510389, (53, 3583): 1123.0879574574851, (53, 3601): 1103.2084287792466, (53, 3656): 1110.007143749742, (53, 3669): 1118.403800703546, (53, 3670): 1114.2383774427428, (53, 3695): 1138.1505647808006, (53, 3696): 1134.8692629171176, (53, 3782): 1126.3134959574863, (53, 3792): 1129.4592672819056, (53, 3989): 3074.3528231540786, (53, 4008): 3097.095021204521, (53, 4031): 3091.476781687463, (53, 4045): 3087.353351312034, (53, 4144): 3092.41261014234, (53, 4145): 3073.6008375786505, (53, 4164): 3084.582027269055, (53, 4168): 3079.375562847416, (53, 4173): 3078.8656151285077, (53, 4181): 3064.9387214492826, (53, 4228): 3047.5156844498138, (53, 4248): 3047.5394608305382, (53, 4254): 2938.016422874853, (53, 4260): 2936.914448538101, (53, 4262): 2946.0624271751904, (53, 4273): 2943.2833926776457, (53, 4319): 2873.7169073452333, (53, 4326): 2870.855265034932, (53, 4328): 2871.4974693703643, (53, 4334): 2877.356303456206, (53, 4335): 2875.743411900841, (53, 4372): 2793.224802259606, (53, 4413): 2863.951578062403, (53, 4434): 2791.1438972504366, (53, 4447): 2804.0681665535985, (53, 4452): 2791.686240461664, (53, 4463): 2617.9133247005043, (53, 4465): 2624.4489940829153, (53, 4619): 2861.6533386253445, (53, 4645): 2880.8839581145453, (53, 4657): 2876.6822383046165, (53, 4666): 2868.591617010096, (53, 4676): 2880.836944353603, (53, 4678): 2884.260541766662, (53, 4689): 2874.1760406811886, (53, 4704): 2934.710161859342, (53, 4726): 3046.4925076539926, (53, 4727): 3044.287439126302, (53, 4730): 3040.137347489417, (53, 4731): 3040.4910553229274, (53, 4734): 3047.676460589576, (53, 4735): 3044.867948959936, (53, 4736): 3045.300783503366, (53, 4737): 3040.7415814280866, (53, 4738): 3040.7331639844156, (53, 4756): 3042.556646714348, (53, 4760): 3034.985451941395, (53, 4761): 3037.640601468222, (53, 4762): 3031.110059034275, (53, 4765): 3035.6533757960947, (53, 4773): 3051.5373763001994, (53, 4774): 3048.3357456614913, (53, 4790): 3050.256034576706, (53, 4795): 3048.6370827576457, (53, 4799): 3048.635275956679, (53, 4801): 3051.559133929018, (53, 4804): 3050.925768860661, (53, 4805): 3049.5757735759635, (53, 4806): 3045.6767003874384, (53, 4815): 3042.475406952173, (53, 4816): 3048.5608188278616, (53, 4817): 3048.224637478254, (53, 4826): 3045.3762649765777, (53, 4830): 3041.635907522817, (53, 4839): 3041.354260739341, (53, 4840): 3042.725372734557, (53, 4841): 3037.5809689834073, (53, 4846): 3036.286026940085, (53, 4848): 3034.574524988912, (53, 4850): 3036.375511703456, (53, 4871): 3016.2193300036506, (53, 4883): 3034.246830143774, (53, 4900): 3026.6574958779443, (53, 4901): 3022.951105173905, (53, 4917): 2837.687721921588, (53, 4931): 2820.1095398497964, (53, 4944): 2840.588364418061, (53, 4956): 2822.427364180222, (53, 4958): 2820.1238271146726, (53, 4959): 2815.5557147524273, (53, 4961): 2826.71907455526, (53, 4966): 2817.092037117012, (53, 5207): 2797.430254071147, (53, 5272): 2514.4302686465853, (53, 5283): 2520.3829609810937, (53, 5287): 2526.243489087232, (53, 5289): 2528.713434498588, (53, 5293): 2519.0465330881016, (53, 5295): 2536.2368974525384, (53, 5296): 2533.9120680355104, (53, 5298): 2532.4763824677766, (53, 5303): 2535.649290814572, (53, 5305): 2506.5965279235097, (53, 5306): 2498.6913304325303, (53, 5307): 2503.2362796366992, (53, 5308): 2508.6825728121385, (53, 5313): 2511.2208950516037, (53, 5314): 2515.9136014120995, (53, 5317): 2507.267750604996, (53, 5319): 2529.205508249163, (53, 5324): 2527.439322109428, (53, 5326): 2526.428224719894, (53, 5348): 2495.3515203607944, (53, 5351): 2496.723011579585, (53, 5399): 2528.906745492303, (53, 5413): 2499.4949038555405, (53, 5422): 2534.4439390509174, (53, 5445): 2519.4280832049253, (53, 5448): 2513.5479618940312, (53, 5456): 2509.797548378732, (53, 5467): 2514.6277046891146, (53, 5624): 2457.5198684663555, (53, 5671): 2678.6332649700557, (53, 5672): 2670.7884346159367, (53, 5797): 2773.684289479453, (53, 5871): 2589.9653640396887, (53, 5976): 2519.621003336692, (53, 6118): 620.5607045669082, (53, 6248): 602.8297971122346, (53, 6345): 2165.141091525369, (53, 6352): 2143.5361204052297, (53, 6354): 2170.360547266559, (53, 6359): 2174.7459913260764, (53, 6376): 2147.3065055249244, (53, 6378): 2167.8101920441527, (53, 6381): 2173.0635167132186, (53, 6383): 2160.5082181108255, (53, 6396): 2171.1893345540816, (53, 6399): 2165.565829141577, (53, 6408): 2144.1874647277377, (53, 6409): 2154.0772703168336, (53, 6419): 2118.7558104358436, (53, 6422): 2146.7891958438017, (53, 6423): 2145.027782097836, (53, 6424): 2167.9552683385486, (53, 6439): 2163.735624082814, (53, 6464): 2157.677073251952, (53, 6465): 2155.5788649463334, (53, 6469): 2158.445250799015, (53, 6470): 2157.162947602884, (53, 6472): 2182.1165816644834, (53, 6480): 2177.2365374014666, (53, 6486): 2190.016618027532, (53, 6497): 2185.69197694099, (53, 6503): 2159.0132290480237, (53, 6508): 2160.5482479209477, (53, 6509): 2164.744987256178, (53, 6521): 2179.8599703333866, (53, 6544): 2178.352176204854, (53, 6552): 2150.236434244136, (53, 6553): 2146.8563822217016, (53, 6554): 2143.4179851415815, (53, 6578): 2155.8937182947743, (53, 6582): 2153.3693677309902, (53, 6601): 2157.430441858285, (53, 6609): 2184.6916223069984, (53, 6610): 2185.638610538149, (53, 6611): 2186.3573996570112, (53, 6614): 2184.633583272319, (53, 6615): 2185.2343804892143, (53, 6616): 2188.7038528175563, (53, 6617): 2187.1715673172944, (53, 6618): 2192.131021060604, (53, 6619): 2182.1569265985727, (53, 6620): 2188.7605792236104, (53, 6621): 2185.8728084981276, (53, 6622): 2186.5574205716457, (53, 6623): 2184.27993136446, (53, 6624): 2181.677017272401, (53, 6625): 2181.1507045527237, (53, 6626): 2182.0151895569015, (53, 6627): 2183.9664639482976, (53, 6628): 2188.1548119197682, (53, 6629): 2182.4531481775134, (53, 6630): 2178.7294176550567, (53, 6632): 2182.16732032267, (53, 6634): 2175.5818184382447, (53, 6635): 2184.8421861145293, (53, 6636): 2188.8595343784013, (53, 6637): 2178.486492653025, (53, 6638): 2179.042840805254, (53, 6639): 2184.235527138094, (53, 6640): 2179.548657738352, (53, 6641): 2185.793422925815, (53, 6642): 2179.0871508393357, (53, 6643): 2181.7233860226397, (53, 6645): 2182.5425551382573, (53, 6646): 2191.1017939088165, (53, 6647): 2179.969706956746, (53, 6653): 2185.1165000793, (53, 6655): 2184.284561536865, (53, 6658): 2175.3522777267744, (53, 6662): 2178.9004769676426, (53, 6819): 2013.9558446165424, (53, 6996): 2072.6531978241337, (53, 7059): 2111.31796314061, (53, 7187): 2058.2071543785114, (53, 7304): 1967.0987498952504, (53, 7528): 2073.9314414645896, (53, 7720): 2299.690874165624, (53, 7793): 2296.7612072461566, (53, 7807): 2299.304012610144, (53, 7808): 2296.064624288697, (53, 7831): 2205.8227390941424, (53, 7850): 2242.472721667314, (53, 7852): 2234.025987682492, (53, 8012): 2286.609313246841, (53, 8125): 2332.679555167236, (53, 8208): 2370.949625687717, (53, 8392): 2236.055093218431, (53, 8651): 1828.0175063765357, (53, 9088): 2001.0131556298822, (53, 9443): 1756.1856133861886, (53, 9444): 1762.1408088309438, (53, 9828): 1604.7699957265397, (53, 9868): 1583.1261176143164, (53, 10180): 2337.459723147473, (53, 10256): 2437.421731672142, (53, 10276): 2389.5931081865747, (53, 10378): 2396.798904505221, (53, 10676): 2313.8123622662733, (53, 10714): 2251.620345227076, (53, 10730): 2255.979347186218, (53, 10862): 2255.9594786698685, (53, 10881): 2271.352777510665, (53, 10883): 2269.2667355642957, (53, 10885): 2252.7460564322764, (53, 10891): 2266.0403759630426, (53, 10909): 2265.5920907408517, (53, 10911): 2268.6802228036404, (53, 10913): 2264.8275871558253, (53, 10915): 2265.146959790373, (53, 10919): 2267.6913775211106, (53, 11037): 2153.1597259703585, (53, 11039): 2118.1067813548616, (53, 11516): 3272.3239035099955, (53, 11856): 2879.7412247252396, (53, 11857): 2877.192542787839, (53, 11861): 2878.626647465653, (53, 11881): 2873.115654349727, (53, 11902): 2856.165854247475, (53, 11911): 2852.0350533982423, (53, 11914): 2854.855543583512, (53, 11922): 2867.8187067996028, (53, 11924): 2871.541126300853, (53, 11926): 2866.596139191612, (53, 11950): 2875.045060953889, (53, 11963): 2891.163899393769, (53, 11983): 2878.2220242029703, (53, 11985): 2899.3522427586095, (53, 12009): 2894.433267286475, (53, 12010): 2883.4513144431057, (53, 12018): 2885.089453216121, (53, 12020): 2888.450772860992, (53, 12021): 2890.1437076802677, (53, 12024): 2901.0570100766545, (53, 12025): 2897.7360939163636, (53, 12027): 2895.0611801113896, (53, 12031): 2881.551740884575, (53, 12032): 2885.6335975843504, (53, 12035): 2893.285280915595, (53, 12041): 2901.747264564279, (53, 12045): 2748.3483031419037, (53, 12145): 2816.2857845902004, (53, 12275): 3076.254117351617, (53, 12294): 3044.026120553995, (53, 12358): 3131.5329318112235, (53, 12463): 3163.524889478665, (53, 12465): 3162.3048516732993, (53, 12482): 3180.269430604121, (53, 12503): 3177.4862721062273, (53, 12506): 3181.738424723087, (53, 12549): 3175.5355338562563, (53, 12559): 3171.6957569477713, (53, 12569): 3174.118619791028, (53, 12572): 3177.377432696753, (53, 12574): 3170.898411400953, (53, 12576): 3179.5916956391497, (53, 12591): 3180.5287163371167, (53, 12608): 3207.6531266137285, (53, 12696): 3167.28404826618, (53, 12710): 3193.7427304341804, (53, 12728): 3179.5482487342524, (53, 12766): 2491.373242387649, (53, 12771): 2466.2502290601647, (53, 12790): 2461.9329073057547, (53, 12795): 2451.3150011812163, (53, 12797): 2415.422835378499, (53, 12798): 2421.02143967224, (53, 12811): 2451.9640457083515, (53, 12830): 2440.5302686362456, (53, 12848): 2448.081808571828, (53, 12850): 2451.9877570639364, (53, 12852): 2439.698463680632, (53, 12854): 2434.9295321632762, (53, 12859): 2453.3914283950617, (53, 12861): 2426.778567700668, (53, 12865): 2456.8774758430914, (53, 12866): 2455.0519654852583, (53, 12867): 2464.0423759254645, (53, 12874): 2459.593333753327, (53, 12875): 2463.4722126967577, (53, 12881): 2447.948960053227, (53, 12883): 2453.922552239956, (53, 12885): 2466.4625112441267, (53, 12888): 2451.6009209858958, (53, 12889): 2450.6782535276084, (53, 12892): 2460.375984256958, (53, 12893): 2451.3871014684696, (53, 12896): 2454.6688726785724, (53, 12906): 2458.0147429243934, (53, 13018): 2404.4976785330064, (53, 13071): 2402.7938207922607, (53, 13131): 2373.2026749013653, (53, 13146): 2406.782314759366, (53, 13159): 2351.620128273321, (53, 13193): 2367.714723465442, (53, 13198): 2315.893245363574, (53, 13292): 2380.900737012578, (53, 13296): 2403.25566749209, (53, 13406): 2275.081394397109, (53, 13407): 2272.790941022467, (53, 13417): 2265.022741139845, (53, 13418): 2270.494058030549, (53, 13438): 2297.7305264229544, (53, 13442): 2303.7815678235556, (53, 13443): 2298.9163338027483, (53, 13764): 1870.1453944708062, (53, 13766): 1876.3107617399928, (53, 13771): 1870.0412969596066, (53, 13783): 1865.505261878372, (53, 13784): 1883.1560238388352, (53, 13792): 1857.8567638183358, (53, 13824): 1861.2061837773854, (53, 14017): 1900.150184424629, (53, 14870): 2274.8220825747385, (53, 14997): 2031.2064740397334, (53, 15000): 2033.095566327525, (53, 15003): 2038.5268236566953, (53, 15006): 2042.1611805108805, (53, 15007): 2046.4658367142981, (53, 15056): 2049.7185341654877, (53, 15063): 2046.7501201098935, (53, 15069): 2046.8458674693522, (53, 15076): 2048.0095413471286, (53, 15086): 2033.3068297699915, (53, 15087): 2030.5363691289772, (53, 15111): 2016.7536737246498, (53, 15116): 2024.792127171829, (53, 15722): 1913.1813096897677, (53, 15998): 1875.0020720248374, (53, 16073): 1061.6703672028739, (53, 16939): 499.423003945498, (53, 16940): 505.62014662784804, (53, 16951): 491.08726039768993, (53, 16963): 492.31150241010005, (53, 16965): 488.0494241190254, (53, 16969): 485.17671299014773, (53, 16970): 492.2149979183616, (53, 16971): 496.3485900696698, (53, 16973): 493.9882237072134, (53, 16974): 483.7392690728586, (53, 16976): 493.6235868946041, (53, 16978): 497.55765075891486, (53, 16980): 494.48626352720305, (53, 16982): 480.9508004685431, (53, 17045): 219.42980182471584, (53, 17048): 211.8184233697138, (53, 17304): 3018.959589999924, (53, 17305): 3012.7122951901397, (53, 17330): 3017.2919109905847, (53, 17334): 3011.3255137727065, (53, 17343): 3022.868556152088, (53, 17345): 3008.7974516979875, (53, 17347): 3015.2708746879393, (53, 17351): 3000.443551975614, (53, 17372): 3009.5893851232518, (53, 17373): 3022.74029622838, (53, 17377): 3023.4796752308325, (53, 17382): 3014.4441135832785, (53, 17383): 3016.874081304511, (53, 17389): 3011.3588018885926, (53, 17400): 3020.92601286709, (53, 17401): 3021.1000190481436, (53, 17402): 3021.244985529957, (53, 17403): 3021.9647129111763, (53, 17440): 3006.9038633047644, (53, 17455): 3019.8002888629835, (53, 17491): 3018.985864498857, (53, 17507): 3010.9580657128213, (53, 17509): 3016.6335358349356, (53, 17590): 2994.5254493886773, (53, 17615): 2980.039998268298, (53, 17642): 2984.1263017715232, (53, 17643): 2982.860484543909, (53, 17668): 2980.34144503141, (53, 17721): 2972.7388344371366, (53, 17754): 3022.6218942663827, (53, 17769): 3015.123721365356, (53, 17776): 2990.702877731822, (53, 17804): 3023.8677038193864, (53, 17809): 3029.04459648886, (53, 17824): 3027.028906385394, (53, 17837): 3005.584954520841, (53, 17838): 3004.8957651284277, (53, 17862): 3000.4515525617235, (53, 17866): 3012.0493882171854, (53, 17872): 2997.5029632347905, (53, 17873): 2988.361313437537, (53, 17881): 3002.2011924907442, (53, 17947): 1053.443058481664, (53, 17951): 1059.052514422726, (53, 17953): 1062.505711398125, (53, 17954): 1063.6659940910417, (53, 17959): 1050.4716165822504, (53, 17963): 1048.3894625063097, (53, 18000): 1085.8919521269354, (53, 18001): 1087.4476164949433, (53, 18111): 1130.3862390363636, (53, 18148): 1289.1755726177055, (53, 18166): 1236.1023050095505, (53, 18189): 1162.4348355983773, (53, 18239): 3026.213243256418, (53, 18240): 3025.869157827225, (53, 18245): 3026.5500430654656, (53, 18247): 3025.1183716629735, (53, 18251): 3026.1864052507494, (53, 18256): 3027.0140500588386, (53, 18258): 3025.5539689822936, (53, 18259): 3025.634625408057, (53, 18260): 3025.92398133185, (53, 18262): 3026.6831622809405, (53, 18263): 3027.192574177436, (53, 18264): 3027.4986205585296, (53, 18266): 3026.8140606018133, (53, 18267): 3027.153170483633, (53, 18268): 3027.213399526144, (53, 18269): 3027.858417967111, (53, 18275): 3027.552861713874, (53, 18285): 3027.506535866382, (53, 18308): 3020.661745916514, (53, 18313): 3017.543537226441, (53, 18314): 3018.0924550980426, (53, 18315): 3028.6137584625844, (53, 18316): 3028.1690531185177, (53, 18317): 3028.446771833729, (53, 18320): 3029.2615965627692, (53, 18321): 3029.2419023463203, (53, 18322): 3029.757181304732, (53, 18324): 3030.7223209208937, (53, 18325): 3032.856222355869, (53, 18326): 3032.078779006802, (53, 18327): 3028.3810249757776, (53, 18329): 3034.241127326116, (53, 18330): 3031.9851269146848, (53, 18331): 3030.7454217862387, (53, 18332): 3029.270864203344, (53, 18333): 3032.103024004053, (53, 18336): 3031.4768526211788, (53, 18337): 3032.4453710215394, (53, 18403): 3029.2143310980687, (53, 18432): 2988.858127953423, (53, 18451): 3016.171179180985, (53, 18466): 3043.701446573591, (53, 18481): 3030.174763167242, (53, 18483): 3029.9074482156843, (53, 18484): 3028.937068569287, (53, 18485): 3026.2816031562716, (53, 18486): 3030.372180116534, (53, 18487): 3027.955822606799, (53, 18489): 3029.151769742783, (53, 18490): 3032.594827349392, (53, 18491): 3033.8823352144045, (53, 18492): 3024.985003005623, (53, 18493): 3030.227251804144, (53, 18494): 3028.415078585807, (53, 18495): 3031.6748154833695, (53, 18496): 3030.109628487072, (53, 18497): 3027.640823472934, (53, 18498): 3027.2031230271887, (53, 18499): 3029.109474730604, (53, 18501): 3028.1930516382063, (53, 18502): 3027.0029387817804, (53, 18503): 3025.771102202777, (53, 18504): 3030.3181675560522, (53, 18506): 3029.126267229373, (53, 18507): 3028.1387808432446, (53, 18508): 3029.0985622830262, (53, 18509): 3029.371510084519, (53, 18510): 3026.167680067198, (53, 18511): 3031.128311213281, (53, 18512): 3029.1890236282748, (53, 18515): 3030.8069067134284, (53, 18516): 3031.7632740099098, (53, 18517): 3030.6323540416533, (53, 18518): 3032.543899101408, (53, 18519): 3030.4309334700074, (53, 18520): 3028.4238684028333, (53, 18522): 3035.1294464560997, (53, 18523): 3035.688542039074, (53, 18532): 3037.8258844146903, (53, 18535): 3033.6799392215535, (53, 18537): 3031.3717072685517, (53, 18539): 3032.003776655503, (53, 18540): 3032.4302720419437, (53, 18541): 3033.6967420725687, (53, 18542): 3034.4736186455107, (53, 18543): 3030.730874628392, (53, 18546): 3032.9924306256826, (53, 18555): 3036.6369138826817, (53, 18556): 3037.4932633698268, (53, 18565): 3037.940780517073, (53, 18567): 3039.562105787094, (53, 18568): 3037.3371632721614, (53, 18577): 3051.4703447416978, (53, 18583): 3048.320391816882, (53, 18605): 3050.354196391029, (53, 18608): 3041.905810019934, (53, 18616): 3063.6088966321267, (53, 18618): 3075.381740698151, (53, 18625): 3069.4600938154713, (53, 18645): 3058.6483587979546, (53, 18646): 3061.931174160605, (53, 18653): 3054.5086936229677, (53, 18654): 3063.657927487512, (53, 18655): 3058.06751165646, (53, 18666): 3091.211374035172, (53, 18837): 3019.137069866936, (53, 18974): 3009.2584368220564, (53, 18999): 3015.1083197678336, (53, 19000): 3018.431011407938, (53, 19174): 2842.375289896788, (53, 19342): 2904.1909878495962, (53, 19455): 2880.126671006231, (53, 19555): 2709.3026536022635, (53, 19564): 2713.3592617202507, (53, 19573): 2707.537904686622, (53, 19586): 2705.3095830208877, (53, 19605): 2708.8557823635706, (53, 19611): 2713.010866601236, (53, 19614): 2712.6699844028985, (53, 19641): 2789.1387772803946, (53, 19702): 2786.0081219357485, (53, 19713): 2780.7806748879098, (53, 19731): 2690.591079560521, (53, 19819): 2851.3759274840427, (53, 19893): 2725.8633352884935, (53, 19899): 2762.6899215504527, (53, 19929): 2735.6248233369474, (53, 19951): 2809.273599426531, (53, 19962): 2741.4785304341353, (53, 19970): 2758.0116214416325, (53, 19971): 2758.278736774761, (53, 19972): 2752.0103540230225, (53, 19975): 2749.138336229702, (53, 19978): 2825.4584074957015, (53, 19987): 2826.8200043790443, (53, 19989): 2806.49449334418, (53, 20039): 2830.604013624879, (53, 20043): 2839.231815566823, (53, 20047): 2832.841967836641, (53, 20052): 2810.2395933385956, (53, 20054): 2811.9540201686896, (53, 20085): 2914.937580462651, (53, 20104): 2921.352270921622, (53, 20132): 2881.9296965289877, (53, 20203): 2720.7216924230033, (53, 20280): 2711.854149286386, (53, 20285): 2709.495404085618, (53, 20290): 2715.521672254487, (53, 20297): 2708.6750947716255, (53, 20309): 2829.4640868651604, (53, 20453): 2936.579879852674, (53, 20485): 2665.508783831399, (53, 20520): 2648.144570795294, (53, 20526): 2641.0418301794643, (53, 20698): 1700.028062447235, (53, 20868): 1490.2780031819896, (53, 21042): 2477.094530477082, (53, 21057): 2519.3540999395523, (53, 21066): 2499.671542986147, (53, 21075): 2490.2316055067477, (53, 21093): 2481.7195353439997, (53, 21098): 2513.8358045359573, (53, 21127): 2481.341664532182, (53, 21130): 2490.026815451391, (53, 21144): 2487.466441854133, (53, 21146): 2478.5707908772197, (53, 21147): 2486.3512861656263, (53, 21148): 2494.174700747924, (53, 21153): 2471.324113391916, (53, 21293): 2549.0486719626524, (53, 21426): 2525.0046981966134, (53, 21442): 2567.508410390128, (53, 21451): 2571.669260141365, (53, 21466): 2546.868803999305, (53, 21469): 2553.838208659301, (53, 21471): 2543.304542263034, (53, 21473): 2549.23244747688, (53, 21475): 2544.114141244806, (53, 21482): 2557.684162257314, (53, 21484): 2556.5265187580912, (53, 21488): 2552.288506315073, (53, 21494): 2544.8432417601443, (53, 21498): 2549.840170799615, (53, 21500): 2542.539957987377, (53, 21514): 2559.0562093353524, (53, 21537): 2542.7978785658884, (53, 21662): 2567.1332437265614, (53, 21691): 2540.458817284866, (53, 21757): 2487.20228426132, (53, 21777): 2399.8170905669904, (53, 21778): 2393.104868081814, (53, 21779): 2397.4964299337657, (53, 21790): 2406.67957752223, (53, 21802): 2407.5805435993493, (53, 21824): 2415.190536077519, (53, 21874): 2400.024099306845, (53, 21879): 2397.2417139202894, (53, 21983): 2419.0632196251418, (53, 22002): 2495.7643652680495, (53, 22132): 2435.064183220436, (53, 22261): 1619.790528029163, (53, 22298): 1638.5862447743023, (53, 22339): 1591.7747637580767, (53, 22508): 1733.328032284676, (53, 22841): 630.9007184450065, (53, 22842): 627.3234606867226, (53, 22874): 616.0316990085729, (53, 22941): 628.0379456400597, (53, 22956): 624.3758285090016, (53, 22960): 632.8088763991052, (53, 22968): 583.3748836742843, (53, 22970): 590.3358408283275, (53, 22974): 559.1519513994426, (53, 22980): 558.4234027668198, (53, 23025): 513.6366321664823, (53, 23028): 504.54983160981106, (53, 23081): 447.35586522103114, (53, 23104): 372.07371601489365, (53, 23147): 519.4300512188365, (53, 23298): 2679.6483918607246, (53, 23376): 2660.692193507516, (53, 23381): 2652.7201887579813, (53, 23529): 2694.5194682038314, (53, 23556): 2683.1225906355826, (53, 23718): 2665.160187025816, (53, 24001): 2791.1690919331763, (53, 24094): 2832.2334532009613, (53, 24129): 2851.075806997695, (53, 24174): 2814.3379860221676, (53, 24235): 2857.8048145211606, (53, 24259): 2874.228098447959, (53, 24260): 2873.1212831933967, (53, 24261): 2868.846616534538, (53, 24305): 2895.0644480937067, (53, 24306): 2899.0361428064252, (53, 24307): 2893.3535365984267, (53, 24308): 2833.7882036079045, (53, 24498): 2937.5749693538414, (53, 24499): 2938.1113598125426, (53, 24500): 2934.4945010129804, (53, 24668): 2904.1192621711843, (53, 24711): 2964.099217453992, (53, 24756): 2979.3575719223504, (53, 24788): 2983.658134107178, (53, 24809): 2965.3332819915267, (53, 24813): 2970.8174027364907, (53, 24821): 2968.9051453025586, (53, 24825): 2970.8033818002345, (53, 24832): 2963.7072307899753, (53, 24833): 2966.781423977731, (53, 24835): 2969.9898448975764, (53, 24837): 2974.536016931309, (53, 24840): 2963.4084466016598, (53, 24841): 2967.7910388027567, (53, 24844): 2963.7886421427697, (53, 24845): 2965.649150183969, (53, 24846): 2966.705645302414, (53, 24849): 2968.496700145523, (53, 24850): 2972.050462776334, (53, 24863): 2927.5587035518442, (53, 24866): 2932.963824553273, (53, 24885): 2940.280004191541, (53, 24886): 2941.279170313437, (53, 24889): 2951.4112734039054, (53, 24903): 2955.2180538610937, (53, 24909): 2933.9287888190033, (53, 24999): 3163.006494723291, (53, 25019): 3154.3831477860203, (53, 25028): 3160.345038345975, (53, 25137): 2723.9587641150088, (53, 25145): 2731.459489398528, (53, 25208): 2816.163584586216, (53, 25233): 2805.9311742632563, (53, 25371): 2725.1812838629435, (53, 25377): 2703.992478064944, (53, 25828): 2320.9948566950566, (53, 25851): 2261.8925412516464, (53, 25874): 2317.429250353789, (53, 25898): 2343.370154537299, (53, 25946): 2314.9947059156143, (53, 26047): 2438.3568367333523, (53, 26066): 2570.929525851579, (53, 26197): 2484.849900546635, (53, 26212): 2140.0252507311834, (53, 26253): 2122.1146309431037, (53, 26254): 2128.474769549486, (53, 26257): 2136.223450537486, (53, 26258): 2126.1434962423505, (53, 26260): 2131.2145683236668, (53, 26266): 2120.972493246378, (53, 26267): 2127.511437857911, (53, 26271): 2128.1377098236662, (53, 26304): 2190.2138294221927, (53, 26305): 2188.619509856359, (53, 26363): 2303.6021809344707, (53, 26441): 1734.8621177781538, (53, 26442): 1733.8981451628654, (53, 26450): 1742.0241469703703, (53, 26459): 1753.1249954558873, (53, 26462): 1756.6701971300938, (53, 26467): 1735.115270354678, (53, 26471): 1735.7261009601916, (53, 26472): 1734.7920845319, (53, 26473): 1733.5198748641835, (53, 26476): 1721.4688045495022, (53, 26485): 1744.1782731219357, (53, 26493): 1738.5471670535355, (53, 26524): 1758.1530546426782, (53, 26525): 1756.0970493828356, (53, 26556): 1739.1673296962351, (53, 26560): 1748.7899830662993, (53, 26561): 1755.5045017083312, (53, 26564): 1738.7477571384793, (53, 26569): 1753.7015718508999, (53, 26570): 1752.1795237584595, (53, 26573): 1746.2613248098908, (53, 26581): 1742.2408450292742, (53, 26583): 1746.4678064175262, (53, 26593): 1736.8994539745493, (53, 26837): 1729.3117337506806, (53, 26844): 1726.4175547618627, (53, 26863): 1722.4297773889925, (53, 26893): 1709.5919723800976, (53, 26902): 1705.2428100256898, (53, 26905): 1719.0053138403816, (53, 26912): 1712.6674912040085, (53, 26921): 1716.9022270484086, (53, 26922): 1711.4015244967195, (53, 27212): 1935.3143691979024, (53, 27218): 1948.6244440162636, (53, 27239): 1928.2565759319596, (53, 27257): 1927.1661432231977, (53, 27274): 1925.2169274899977, (53, 27279): 1921.744766495796, (53, 27282): 1924.8691851522456, (53, 27283): 1931.3794271978193, (53, 27285): 1921.4222835924095, (53, 27286): 1917.3000274763165, (53, 27290): 1926.909281686521, (53, 27295): 1934.7655861063379, (53, 27300): 1926.265996904822, (53, 27344): 1916.7529598190974, (53, 27366): 1909.2418110590556, (53, 27383): 1912.759823665924, (53, 27398): 1918.7931249024402, (53, 27406): 1924.7577768721158, (53, 27407): 1927.0771140930372, (53, 27426): 1958.2321051759527, (53, 27432): 1962.954110886487, (53, 27460): 1963.5811871300234, (53, 27523): 1846.7568217956145, (53, 27545): 1864.0925152358402, (53, 27602): 1774.7211307358614, (53, 27606): 1779.1824657434943, (53, 27646): 1768.0810933267906, (53, 27667): 1750.0138460451321, (53, 27672): 1752.2489402086835, (53, 27674): 1753.322130564103, (53, 27688): 1763.2833839910522, (53, 27692): 1745.5391752796297, (53, 27693): 1747.5437171800497, (53, 27705): 1744.0806967251535, (53, 27712): 1740.0431178869835, (53, 27786): 1909.8448307295228, (53, 27790): 1962.5286886189976, (53, 27791): 1969.7895671718416, (53, 27795): 1908.5285129079784, (53, 27801): 1943.4662252568282, (53, 27813): 1902.8914401123243, (53, 27816): 1914.1517729633897, (53, 27823): 1945.2093143466773, (53, 27830): 1927.2067145078256, (53, 27884): 1764.2104965175408, (53, 27885): 1770.3068255654314, (53, 27896): 1768.1765811052244, (53, 27919): 1771.3430232108353, (53, 27922): 1767.1511697590374, (53, 27930): 1769.2317544296652, (53, 27934): 1766.486407512227, (53, 27935): 1763.2612442042596, (53, 27948): 1608.879830415186, (53, 27951): 1660.779618684284, (53, 28061): 1358.950315208395, (53, 28290): 1182.8468375658763, (53, 28292): 1164.996163608257, (53, 28293): 1178.2084828828906, (53, 28295): 1170.4214409605656, (53, 28296): 1178.0791856073185, (53, 28297): 1191.3116902073357, (53, 28302): 1184.1637726389426, (53, 28310): 709.1215464145134, (53, 28313): 707.3941394280789, (53, 28372): 698.6480351704646, (53, 28398): 698.4817971387945, (53, 28399): 701.4858895913079, (53, 28400): 697.4635346294631, (53, 28401): 707.2527001440624, (53, 28445): 714.081083811417, (53, 28475): 712.1004102096487, (53, 28885): 2861.530955888295, (53, 28886): 2857.9953271433897, (53, 28915): 2861.3932657619266, (53, 28916): 2858.2512291116773, (53, 28917): 2856.3534284992993, (53, 28921): 2868.18181253633, (53, 28931): 2867.2845368112467, (53, 28945): 2850.278780222838, (53, 28982): 2854.3876131665443, (53, 29219): 2875.9882950108263, (53, 29228): 2859.717076165014, (53, 29246): 2965.4315970212147, (53, 29248): 2963.9939884058294, (53, 29282): 2942.076361051265, (53, 29290): 2976.1174220508506, (53, 29291): 2971.7418811092375, (53, 29292): 2975.8487154199306, (53, 29293): 2967.2774594764956, (53, 29294): 2974.120732605051, (53, 29298): 2967.9426757592933, (53, 29299): 2967.2241265530156, (53, 29304): 2959.179884903981, (53, 29317): 2938.57626198561, (53, 29323): 2936.9730888477984, (53, 29330): 2946.905642042168, (53, 29331): 2951.8195723367817, (53, 29344): 2878.047860605255, (53, 29445): 2691.8934129262047, (53, 29724): 776.4704637631603, (53, 29738): 776.0054136172291, (53, 29745): 782.7822969149743, (53, 29748): 809.8010048805213, (53, 29750): 820.5760750939097, (53, 29759): 807.0857358230361, (53, 29772): 805.8763903008539, (53, 29781): 806.9110939531042, (53, 29784): 795.3998050122882, (53, 29790): 811.4719131397122, (53, 29811): 824.2135962189587, (53, 29817): 893.4974046174581, (53, 29818): 894.8605632453964, (53, 29929): 765.9180276487953, (53, 30039): 683.4234955887839, (53, 30066): 643.0053808700883, (53, 30116): 727.0699252629117, (53, 30238): 860.5033809968498, (53, 30248): 721.5364009241821, (53, 30260): 713.6863765618082, (53, 30545): 2804.089472018264, (53, 30733): 2627.365406707159, (53, 30756): 2586.4665881215096, (53, 30921): 2668.9344093586597, (53, 31079): 2178.245502525348, (53, 31149): 2166.4041438227077, (53, 31154): 2165.042958160987, (53, 31160): 2165.3504761627614, (53, 31163): 2162.4147289441676, (53, 31189): 2097.23797700961, (53, 31215): 2099.347400718319, (53, 31259): 2082.4813374876217, (53, 31262): 2075.912607758022, (53, 31430): 2179.8651616807997, (53, 31568): 1973.0908124707391, (53, 31751): 2136.92804972841, (55, 109): 2451.176601149632, (55, 872): 1315.2337628408357, (55, 873): 1312.5270711466576, (55, 877): 1309.394123308584, (55, 879): 1308.5887380307142, (55, 884): 1302.0798661517101, (55, 889): 1302.3189291733254, (55, 891): 1304.1056818522509, (55, 892): 1307.3613569329045, (55, 894): 1309.399493657938, (55, 896): 1318.8758762705233, (55, 903): 1304.5603904412455, (55, 909): 1322.7852553364055, (55, 910): 1325.5247372651165, (55, 912): 1326.4282277587513, (55, 913): 1326.040041717476, (55, 916): 1331.4660854099666, (55, 926): 1329.683258695294, (55, 927): 1331.4443999637776, (55, 948): 1305.7797392162556, (55, 961): 1320.7989404474438, (55, 962): 1323.1699395026196, (55, 963): 1324.9735408904398, (55, 967): 1305.0976973167624, (55, 974): 1296.8857063013393, (55, 998): 1300.6179333745608, (55, 1014): 1304.0780894808665, (55, 1086): 1433.317982588403, (55, 1087): 1447.3533913954852, (55, 1089): 1442.2661515488653, (55, 1090): 1440.172961565938, (55, 1092): 1436.8714438195902, (55, 1097): 1436.6731159406831, (55, 1107): 1443.9860422656147, (55, 1387): 2079.212812446531, (55, 1554): 2130.0597753372053, (55, 1827): 1138.9957200567017, (55, 1828): 1140.9608792208294, (55, 1829): 1139.4326805151688, (55, 1830): 1129.910659720294, (55, 1831): 1131.5538629031535, (55, 1832): 1132.5796333624833, (55, 1833): 1134.2262822678742, (55, 1836): 1136.1908391500967, (55, 1841): 1133.2092298619107, (55, 1843): 1133.4359351649064, (55, 1844): 1131.6905851570411, (55, 1845): 1130.5193628073496, (55, 1847): 1136.2970511065623, (55, 1848): 1135.3772495316903, (55, 1849): 1129.513224635493, (55, 1850): 1130.6092539399317, (55, 1851): 1130.275785461346, (55, 1852): 1126.4050314887245, (55, 1854): 1128.9874467881793, (55, 1856): 1131.3750670174097, (55, 1857): 1133.3545469616445, (55, 1858): 1132.5659175429355, (55, 1861): 1136.192471104173, (55, 1866): 1128.1319009727983, (55, 1867): 1136.4198209567207, (55, 1868): 1139.7273763414842, (55, 1870): 1126.7921403316084, (55, 1871): 1139.6797937539309, (55, 1875): 1131.6075958163976, (55, 1880): 1134.2759291588272, (55, 1882): 1128.5925439619568, (55, 1883): 1134.9337729765584, (55, 1889): 1140.2856423310614, (55, 1893): 1145.6528080513317, (55, 1894): 1147.0626128432777, (55, 1899): 1143.1951928138933, (55, 1900): 1144.255309063031, (55, 1902): 1145.1063864516318, (55, 1905): 1142.202623064613, (55, 1907): 1138.8923371641908, (55, 1910): 1143.458920174938, (55, 1917): 1153.8877216739534, (55, 1920): 1142.2284176118085, (55, 1935): 1149.5093098903567, (55, 1937): 1147.9218121464708, (55, 1946): 1152.5608927318926, (55, 1949): 1154.2314419474935, (55, 1950): 1145.5837918936581, (55, 1951): 1147.6423431785352, (55, 1952): 1137.442563051834, (55, 1953): 1146.42072412253, (55, 1954): 1139.9477320031199, (55, 1958): 1150.1816114118585, (55, 1960): 1147.3080171375466, (55, 1968): 1146.200430623876, (55, 1969): 1156.875352877515, (55, 1974): 1153.3996742597715, (55, 1975): 1150.9109759636622, (55, 1979): 1156.0067930506225, (55, 1980): 1148.5873030651549, (55, 1981): 1153.2085520649878, (55, 1985): 1155.2341054767242, (55, 1994): 1128.797519318715, (55, 2011): 1126.0674232399276, (55, 2019): 1114.4578304028564, (55, 2020): 1115.9164762663008, (55, 2029): 1114.2814578721457, (55, 2030): 1117.0477077061776, (55, 2032): 1110.2877969680692, (55, 2033): 1114.7875810862363, (55, 2034): 1111.1256715172751, (55, 2036): 1095.6697843433324, (55, 2037): 1100.1954414526087, (55, 2038): 1117.3432453633234, (55, 2042): 1112.2646567349182, (55, 2050): 1120.3461391607389, (55, 2051): 1116.4794663806397, (55, 2053): 1118.0695666805104, (55, 2054): 1117.4672976193606, (55, 2066): 1118.0058685998517, (55, 2067): 1120.0213546113996, (55, 2071): 1131.6978100000495, (55, 2072): 1133.8512283830567, (55, 2073): 1145.960026640338, (55, 2074): 1143.5755846056732, (55, 2080): 1138.60527101273, (55, 2082): 1134.1439349424222, (55, 2083): 1135.5128055592002, (55, 2089): 1138.8796301607238, (55, 2090): 1140.8171219788217, (55, 2092): 1143.3244500444214, (55, 2098): 1143.152213140753, (55, 2099): 1140.4965450933487, (55, 2101): 1139.8024674806297, (55, 2102): 1142.7992059052465, (55, 2103): 1140.4427249687262, (55, 2104): 1137.5434219248086, (55, 2106): 1133.8329408268141, (55, 2112): 1136.9990029661033, (55, 2113): 1141.1266113624654, (55, 2114): 1135.9307755390848, (55, 2117): 1131.2543108537714, (55, 2123): 1264.3919281900419, (55, 2124): 1265.1068175069981, (55, 2134): 1253.9853530917035, (55, 2138): 1259.700738588649, (55, 2141): 1257.0269608795215, (55, 2148): 1222.7287199020518, (55, 2150): 1253.6696969270886, (55, 2151): 1251.7966050156413, (55, 2152): 1250.896428004333, (55, 2153): 1226.326232578993, (55, 2154): 1225.7654568462692, (55, 2155): 1219.4974146709446, (55, 2156): 1223.263093894625, (55, 2157): 1202.2048088143708, (55, 2160): 1243.6680310891768, (55, 2161): 1247.2835890356287, (55, 2162): 1213.0494294000482, (55, 2163): 1213.2962185363394, (55, 2164): 1211.08842689879, (55, 2168): 1235.8526046681193, (55, 2172): 1220.2976802607604, (55, 2174): 1247.2762576116127, (55, 2178): 1216.0911681555472, (55, 2179): 1214.3302540525806, (55, 2183): 1255.5626223070442, (55, 2185): 1253.4226807650864, (55, 2186): 1254.0176480632913, (55, 2190): 1247.6735107643217, (55, 2192): 1247.9832930444843, (55, 2193): 1256.9835746825797, (55, 2194): 1257.2900343967285, (55, 2195): 1252.6533459496616, (55, 2197): 1245.6234362637276, (55, 2205): 1239.4529515726408, (55, 2207): 1232.954579695602, (55, 2208): 1235.6490193954294, (55, 2212): 1267.1714907133376, (55, 2214): 1192.9354900024225, (55, 2225): 1179.5919256325642, (55, 2231): 1277.9518190713368, (55, 2278): 1148.677476701085, (55, 2284): 1140.9479578577186, (55, 2285): 1137.8921622149714, (55, 2291): 1117.9373286424388, (55, 2292): 1142.4670418887633, (55, 2307): 1140.4515279834034, (55, 2313): 1110.3481725022598, (55, 2317): 1152.6407943298339, (55, 2319): 1139.9383442328497, (55, 2321): 1135.7337234844215, (55, 2323): 1142.6876038010828, (55, 2326): 1155.2067305254243, (55, 2327): 1155.315587783963, (55, 2329): 1154.6798171017617, (55, 2330): 1152.324962197851, (55, 2332): 1148.8555163400754, (55, 2344): 1159.180063309104, (55, 2346): 1154.3396121445933, (55, 2361): 1194.8858343537968, (55, 2368): 1170.7971805526684, (55, 2374): 1167.018247769443, (55, 2375): 1169.4552924191926, (55, 2377): 1173.2465545610885, (55, 2378): 1167.3422064028173, (55, 2379): 1162.4198379062977, (55, 2380): 1165.8853830052408, (55, 2383): 1176.130989435717, (55, 2385): 1177.7881665374089, (55, 2395): 1182.1350792520825, (55, 2397): 1160.2362524621915, (55, 2398): 1173.9476432297117, (55, 2399): 1175.9696093831167, (55, 2400): 1176.1245647273204, (55, 2402): 1162.0494107147526, (55, 2403): 1161.5599228436288, (55, 2404): 1163.4463683601587, (55, 2405): 1162.8259298243363, (55, 2407): 1166.2418398246894, (55, 2408): 1163.5960531624316, (55, 2409): 1163.7748458181543, (55, 2411): 1153.4022430221996, (55, 2412): 1156.5902730527025, (55, 2413): 1155.0727063838679, (55, 2414): 1154.611308497992, (55, 2422): 1150.7028682721134, (55, 2424): 1158.2442863499607, (55, 2426): 1159.8019779923538, (55, 2433): 1157.44986885569, (55, 2436): 1152.3334556630125, (55, 2437): 1156.6076101474914, (55, 2440): 1157.093377968535, (55, 2445): 1103.4790995774963, (55, 2447): 1108.9607699550438, (55, 2454): 1108.345690821013, (55, 2455): 1112.2553652975741, (55, 2460): 1109.1752750914234, (55, 2461): 1108.6493382706476, (55, 2471): 1083.870795119864, (55, 2492): 933.4201364408339, (55, 2511): 961.3411447637848, (55, 2523): 946.4075857103053, (55, 2525): 938.4732525996733, (55, 2535): 1018.9520360479798, (55, 2537): 1016.8263914239863, (55, 2538): 1022.2077458086951, (55, 2539): 1002.9414713823998, (55, 2540): 1019.4389625527621, (55, 2542): 1014.250053003468, (55, 2559): 1062.2371476905214, (55, 2575): 1037.813821560856, (55, 2599): 1084.780408030127, (55, 2600): 1071.9129515554102, (55, 2607): 1094.093970667762, (55, 2627): 891.7773309419503, (55, 2647): 877.856004344618, (55, 2674): 899.1326846818693, (55, 2681): 889.0992646879376, (55, 2683): 893.316635726152, (55, 2686): 898.6468745771614, (55, 2689): 891.6192971628216, (55, 2690): 889.20188020291, (55, 2713): 818.1053463795159, (55, 2714): 808.4134767862706, (55, 2715): 809.2646314746254, (55, 2739): 811.4332566264804, (55, 2740): 834.0422450039638, (55, 2741): 836.389346214161, (55, 2749): 799.8477361183225, (55, 2750): 803.6176392899766, (55, 2752): 805.8034978593828, (55, 2755): 804.2338076765499, (55, 2758): 801.0865422639966, (55, 2759): 802.6697684121178, (55, 2769): 805.7345924197485, (55, 2771): 828.0450820173553, (55, 2779): 802.6080199823422, (55, 2784): 784.1157932260658, (55, 2800): 760.0945217137296, (55, 2802): 818.9727458726308, (55, 2803): 821.9328857306249, (55, 2804): 822.7683744053038, (55, 2805): 809.838548044907, (55, 2807): 813.0474975649511, (55, 2809): 805.5476213892669, (55, 2812): 809.7835816776759, (55, 2814): 783.8642721170803, (55, 2817): 755.1021942457999, (55, 2819): 821.0940468456507, (55, 2823): 782.104263678716, (55, 2832): 806.0677528012759, (55, 2836): 803.6316985942257, (55, 2839): 816.3357591306186, (55, 2841): 769.8791553358353, (55, 2843): 774.8577260429454, (55, 2846): 791.008134904086, (55, 2849): 800.9962763845637, (55, 2852): 802.4895223183629, (55, 2853): 800.1133592779079, (55, 2876): 785.2959471650743, (55, 2877): 785.2654081935931, (55, 2885): 755.3820996000114, (55, 2918): 842.1946674358559, (55, 2921): 839.1478250620819, (55, 2925): 864.190145406772, (55, 2926): 878.7161309085634, (55, 2930): 829.2915462668111, (55, 2931): 855.5229974535686, (55, 2938): 836.5470871004948, (55, 2940): 865.6148857872984, (55, 2947): 869.9753315692166, (55, 2949): 842.0698908590239, (55, 2950): 836.8400913255772, (55, 2952): 836.3165931530297, (55, 2958): 838.5387822655756, (55, 2959): 845.3285886769401, (55, 2960): 843.987634545695, (55, 2961): 841.0431379827822, (55, 2963): 835.0154596926407, (55, 2968): 831.9320107870553, (55, 2976): 838.3011414104371, (55, 2981): 792.0245508591877, (55, 2982): 785.2394187276645, (55, 2984): 783.4010534553984, (55, 3003): 775.5461802690448, (55, 3046): 847.5100379985346, (55, 3050): 814.382892858044, (55, 3051): 817.1328828422603, (55, 3053): 813.7153788217101, (55, 3069): 806.7239511167877, (55, 3071): 828.6749936811101, (55, 3080): 744.4288943980263, (55, 3199): 734.3292024197609, (55, 3200): 729.0597625946015, (55, 3205): 738.5743816646003, (55, 3209): 728.7525374816607, (55, 3215): 732.7342596939061, (55, 3217): 730.7420629544322, (55, 3249): 736.7294549715504, (55, 3263): 755.2156515540147, (55, 3289): 751.9811848631741, (55, 3301): 743.0720931997676, (55, 3302): 745.7646984877823, (55, 3307): 745.803444440845, (55, 3310): 744.001909543917, (55, 3391): 566.5984991763493, (55, 3509): 1208.7748926442266, (55, 3510): 1212.1403484520492, (55, 3511): 1212.4589677865613, (55, 3512): 1216.7799118296407, (55, 3514): 1218.1180042676133, (55, 3519): 1188.4098369784006, (55, 3536): 1207.4158112759392, (55, 3545): 1204.8587675742644, (55, 3548): 1213.3460876829226, (55, 3572): 1202.3757355659807, (55, 3581): 1197.8933295851464, (55, 3583): 1210.7102406916638, (55, 3601): 1178.108532720425, (55, 3656): 1174.0991631708637, (55, 3669): 1161.0345548401951, (55, 3670): 1157.0056173733428, (55, 3695): 1183.4262430528854, (55, 3696): 1181.2400002601933, (55, 3782): 1259.252090405279, (55, 3792): 1255.3011819339092, (55, 3989): 2854.4579594604506, (55, 4008): 2872.893214407885, (55, 4031): 2863.0326397893377, (55, 4045): 2864.7401675336337, (55, 4144): 2873.832599534651, (55, 4145): 2864.009630657524, (55, 4164): 2868.759281137898, (55, 4168): 2867.077230626397, (55, 4173): 2867.9324482166667, (55, 4181): 2856.619959896566, (55, 4228): 2836.7698880903035, (55, 4248): 2844.53289421797, (55, 4254): 2780.336915547554, (55, 4260): 2776.8612106440237, (55, 4262): 2785.875876726923, (55, 4273): 2781.9852320463615, (55, 4319): 2740.1228336600484, (55, 4326): 2737.270045153265, (55, 4328): 2737.0509637391287, (55, 4334): 2743.7124729381126, (55, 4335): 2742.9302622246946, (55, 4372): 2893.895432139342, (55, 4413): 2975.221509593703, (55, 4434): 2889.922295014601, (55, 4447): 2898.300203863873, (55, 4452): 2891.344733673061, (55, 4463): 2741.624541283044, (55, 4465): 2746.4010864665042, (55, 4619): 2989.5403392549897, (55, 4645): 3005.6867755093, (55, 4657): 3003.603802472156, (55, 4666): 2997.5489326950837, (55, 4676): 3009.3307036346496, (55, 4678): 3011.6934896028024, (55, 4689): 3004.323815444055, (55, 4704): 3062.9119968553814, (55, 4726): 3212.4910132056984, (55, 4727): 3209.78339927524, (55, 4730): 3204.5239634901914, (55, 4731): 3206.0772356761595, (55, 4734): 3208.7679818079782, (55, 4735): 3206.243646441827, (55, 4736): 3207.5769338305104, (55, 4737): 3203.0698919451866, (55, 4738): 3203.707415109899, (55, 4756): 3206.4384082156184, (55, 4760): 3192.6213115110877, (55, 4761): 3194.064877970486, (55, 4762): 3188.9644666036006, (55, 4765): 3193.984586794276, (55, 4773): 3217.787898161849, (55, 4774): 3215.360784296341, (55, 4790): 3215.990577596066, (55, 4795): 3213.6277393177347, (55, 4799): 3216.5229845034696, (55, 4801): 3222.160918824393, (55, 4804): 3214.556283752511, (55, 4805): 3212.6125166975253, (55, 4806): 3214.3102568236386, (55, 4815): 3211.7015181036777, (55, 4816): 3218.4853511186056, (55, 4817): 3219.7975050445443, (55, 4826): 3215.773540950936, (55, 4830): 3211.9212125786253, (55, 4839): 3200.525351407353, (55, 4840): 3202.9514080310337, (55, 4841): 3197.242629474472, (55, 4846): 3195.3603385984147, (55, 4848): 3194.7566297868257, (55, 4850): 3197.221741691374, (55, 4871): 3165.6156910621776, (55, 4883): 3189.5333740753986, (55, 4900): 3177.192108455182, (55, 4901): 3173.8392715466384, (55, 4917): 2989.432679847203, (55, 4931): 2969.609263852626, (55, 4944): 2991.6832514173643, (55, 4956): 2973.242112694376, (55, 4958): 2972.6585247495473, (55, 4959): 2968.887002911355, (55, 4961): 2977.2588642548803, (55, 4966): 2968.3931256919436, (55, 5207): 2946.4282648790463, (55, 5272): 2555.234193336721, (55, 5283): 2562.8333086127323, (55, 5287): 2575.9548347999325, (55, 5289): 2579.311202937383, (55, 5293): 2555.560899492392, (55, 5295): 2576.6970354447826, (55, 5296): 2577.186120284846, (55, 5298): 2577.287549220594, (55, 5303): 2584.035632622891, (55, 5305): 2552.1305115158807, (55, 5306): 2547.178728789153, (55, 5307): 2548.2769474967527, (55, 5308): 2555.8003211278424, (55, 5313): 2554.6727918223373, (55, 5314): 2559.1824762175847, (55, 5317): 2556.258285302098, (55, 5319): 2576.936723613618, (55, 5324): 2572.2099104549484, (55, 5326): 2569.122904459504, (55, 5348): 2545.9744726895647, (55, 5351): 2552.3895565878524, (55, 5399): 2584.421492411011, (55, 5413): 2563.2292895895994, (55, 5422): 2587.892326715448, (55, 5445): 2571.01303223751, (55, 5448): 2563.8759289884956, (55, 5456): 2562.8441266622103, (55, 5467): 2569.638282161885, (55, 5624): 2488.743534181568, (55, 5671): 2713.0111147729835, (55, 5672): 2703.066908452069, (55, 5797): 2830.3705676077107, (55, 5871): 2688.5577374626287, (55, 5976): 2605.642797768703, (55, 6118): 614.6358890115436, (55, 6248): 469.5833614580964, (55, 6345): 2016.622367737496, (55, 6352): 1993.1349019167494, (55, 6354): 2023.2756267361085, (55, 6359): 2026.299436754826, (55, 6376): 1992.9161296011703, (55, 6378): 2020.3046073235148, (55, 6381): 2023.2566085382846, (55, 6383): 2012.2881695211222, (55, 6396): 2014.2907298049206, (55, 6399): 2014.9717814890296, (55, 6408): 1995.6132159632596, (55, 6409): 2011.002105922101, (55, 6419): 1980.136303041389, (55, 6422): 2002.1113506206857, (55, 6423): 2000.4621499246794, (55, 6424): 2025.854452842377, (55, 6439): 2022.777076688696, (55, 6464): 2017.6719293669476, (55, 6465): 2013.8106166144319, (55, 6469): 2013.5453745903976, (55, 6470): 2011.3781391454415, (55, 6472): 2033.6322152629723, (55, 6480): 2035.975705818957, (55, 6486): 2057.8425012844436, (55, 6497): 2050.8680779875817, (55, 6503): 2028.420845836213, (55, 6508): 2025.0429699154981, (55, 6509): 2031.8478127946134, (55, 6521): 2042.2367534802547, (55, 6544): 2045.3924686317755, (55, 6552): 2014.1180561417225, (55, 6553): 2010.9869107071806, (55, 6554): 2007.7381073126544, (55, 6578): 2018.6590659760477, (55, 6582): 2021.253417139439, (55, 6601): 2021.1613630700515, (55, 6609): 2042.4128718890152, (55, 6610): 2044.3905389115876, (55, 6611): 2042.3829198155336, (55, 6614): 2039.067640508198, (55, 6615): 2040.6042187902267, (55, 6616): 2047.543081117684, (55, 6617): 2044.793711267227, (55, 6618): 2053.2463992129183, (55, 6619): 2037.1723069204988, (55, 6620): 2049.2861851068506, (55, 6621): 2046.787348336297, (55, 6622): 2046.2915019727702, (55, 6623): 2040.5570933224958, (55, 6624): 2039.7573926801829, (55, 6625): 2038.3277048589407, (55, 6626): 2036.2961244799503, (55, 6627): 2036.9374468518404, (55, 6628): 2050.410571105357, (55, 6629): 2042.59797289211, (55, 6630): 2033.2327317662914, (55, 6632): 2041.377369116477, (55, 6634): 2031.2077815655543, (55, 6635): 2044.8587579123523, (55, 6636): 2048.2807923644705, (55, 6637): 2038.8785567450666, (55, 6638): 2035.148790606839, (55, 6639): 2038.185587094163, (55, 6640): 2034.7941992964136, (55, 6641): 2048.033381148522, (55, 6642): 2036.3174812941334, (55, 6643): 2034.8078774561573, (55, 6645): 2038.3195109828368, (55, 6646): 2050.903922078705, (55, 6647): 2036.5633001209674, (55, 6653): 2039.968993756439, (55, 6655): 2037.6871593818466, (55, 6658): 2031.6420396626245, (55, 6662): 2037.342471031571, (55, 6819): 1899.7334227210958, (55, 6996): 1982.6946641115483, (55, 7059): 2018.592974159634, (55, 7187): 2028.4931010097464, (55, 7304): 1910.5415457676038, (55, 7528): 2009.3373840122674, (55, 7720): 2200.1478969451596, (55, 7793): 2206.3542744521774, (55, 7807): 2205.8262970694364, (55, 7808): 2207.7752987957947, (55, 7831): 2074.7140787256585, (55, 7850): 2101.854118360289, (55, 7852): 2091.3570357640933, (55, 8012): 2175.149426804145, (55, 8125): 2280.225604845922, (55, 8208): 2269.3439215969506, (55, 8392): 2129.949641738199, (55, 8651): 1728.8932436280697, (55, 9088): 1852.4379895641664, (55, 9443): 1766.0347377708601, (55, 9444): 1772.6869453694953, (55, 9828): 1685.811155721746, (55, 9868): 1623.027891903706, (55, 10180): 2288.7637645579316, (55, 10256): 2386.914746686369, (55, 10276): 2332.868577763026, (55, 10378): 2316.5523978462516, (55, 10676): 2302.040567156376, (55, 10714): 2253.4963005726963, (55, 10730): 2230.596899319089, (55, 10862): 2465.4046391284696, (55, 10881): 2480.655300157379, (55, 10883): 2479.398190297064, (55, 10885): 2462.0151838014863, (55, 10891): 2477.4823854996957, (55, 10909): 2475.1112340811496, (55, 10911): 2476.18896153035, (55, 10913): 2473.0116060409373, (55, 10915): 2472.3051772891718, (55, 10919): 2473.967892432489, (55, 11037): 2385.0137818432927, (55, 11039): 2341.248705536017, (55, 11516): 2967.3905654186733, (55, 11856): 2745.955015334529, (55, 11857): 2746.9668778901896, (55, 11861): 2746.682148167583, (55, 11881): 2737.2657756573467, (55, 11902): 2721.476425261983, (55, 11911): 2714.351076066542, (55, 11914): 2718.407831969311, (55, 11922): 2731.6201304339424, (55, 11924): 2734.244820472137, (55, 11926): 2729.443948594385, (55, 11950): 2733.714606350107, (55, 11963): 2749.253603311552, (55, 11983): 2731.2452980174235, (55, 11985): 2757.446003658783, (55, 12009): 2747.827765257845, (55, 12010): 2738.475872614639, (55, 12018): 2739.384515360953, (55, 12020): 2743.321141454593, (55, 12021): 2744.404577751193, (55, 12024): 2754.874437735328, (55, 12025): 2752.693461653581, (55, 12027): 2749.8781986742606, (55, 12031): 2736.682954629398, (55, 12032): 2741.375633404692, (55, 12035): 2745.5926184687128, (55, 12041): 2762.638558361478, (55, 12045): 2611.2432319691793, (55, 12145): 2670.658482628185, (55, 12275): 2845.3237016711623, (55, 12294): 2809.1040210643314, (55, 12358): 2887.4424472517985, (55, 12463): 2912.538219066668, (55, 12465): 2911.047175126859, (55, 12482): 2933.1150131252325, (55, 12503): 2929.232803053873, (55, 12506): 2933.448676353117, (55, 12549): 2932.9056448218125, (55, 12559): 2927.9744047635822, (55, 12569): 2928.388586571626, (55, 12572): 2931.7354860779687, (55, 12574): 2925.688695427535, (55, 12576): 2937.6121871325486, (55, 12591): 2941.783745229618, (55, 12608): 2971.2578471447373, (55, 12696): 2933.080094745784, (55, 12710): 2963.84173547046, (55, 12728): 2945.012217070048, (55, 12766): 2289.5752831368936, (55, 12771): 2279.7701420167627, (55, 12790): 2275.4591634836393, (55, 12795): 2263.3342168350664, (55, 12797): 2239.8252670587835, (55, 12798): 2245.2007982660707, (55, 12811): 2271.3741815260987, (55, 12830): 2259.2083808066877, (55, 12848): 2270.634887359203, (55, 12850): 2276.97356951566, (55, 12852): 2260.000068506793, (55, 12854): 2255.9153396607626, (55, 12859): 2276.50058946607, (55, 12861): 2251.2406722803066, (55, 12865): 2273.3997908707765, (55, 12866): 2273.297390961102, (55, 12867): 2279.7049919380293, (55, 12874): 2276.3149390313515, (55, 12875): 2280.2760519656977, (55, 12881): 2265.258443574301, (55, 12883): 2270.5597913891115, (55, 12885): 2282.5147895584555, (55, 12888): 2269.530666406609, (55, 12889): 2269.695308487352, (55, 12892): 2276.425339694483, (55, 12893): 2268.3405508106603, (55, 12896): 2272.18422465187, (55, 12906): 2270.497531001215, (55, 13018): 2197.866982243769, (55, 13071): 2190.593296678618, (55, 13131): 2187.746604308391, (55, 13146): 2222.062378906663, (55, 13159): 2143.342091052483, (55, 13193): 2184.6595593933366, (55, 13198): 2149.236618958904, (55, 13292): 2208.965178224928, (55, 13296): 2239.099940345352, (55, 13406): 2096.7018172889234, (55, 13407): 2093.343876839599, (55, 13417): 2075.8667949043315, (55, 13418): 2078.9842305342668, (55, 13438): 2111.4087150463793, (55, 13442): 2120.2875594245497, (55, 13443): 2115.5149848755877, (55, 13764): 1646.850975624367, (55, 13766): 1652.7082633980658, (55, 13771): 1642.2969727967072, (55, 13783): 1649.9185527439204, (55, 13784): 1661.129469278854, (55, 13792): 1623.9774580147998, (55, 13824): 1644.9569446408857, (55, 14017): 1707.5448921719362, (55, 14870): 2442.4233030999094, (55, 14997): 2008.957063777478, (55, 15000): 2012.9263735596164, (55, 15003): 2020.0444985844745, (55, 15006): 2013.1921773503925, (55, 15007): 2017.27855958782, (55, 15056): 2027.0307903541054, (55, 15063): 2025.7261884794852, (55, 15069): 2028.407466643747, (55, 15076): 2020.2799354674469, (55, 15086): 2004.1988540204075, (55, 15087): 2004.9446063657588, (55, 15111): 1990.3379359343335, (55, 15116): 1999.0728156712453, (55, 15722): 1898.1216571610241, (55, 15998): 1927.224959902563, (55, 16073): 781.8502986307682, (55, 16939): 1038.292484030974, (55, 16940): 1041.0385453239292, (55, 16951): 1025.3167002771515, (55, 16963): 1028.163154969279, (55, 16965): 1030.3978878849648, (55, 16969): 1023.2628000729254, (55, 16970): 1031.4154442561085, (55, 16971): 1029.8915213423932, (55, 16973): 1025.2638512359538, (55, 16974): 1026.9490302236886, (55, 16976): 1034.4129747831946, (55, 16978): 1034.8742224028379, (55, 16980): 1038.8687750017693, (55, 16982): 1022.1859665586721, (55, 17045): 677.8891962824807, (55, 17048): 678.0116746899452, (55, 17304): 2827.816984045158, (55, 17305): 2818.879819080154, (55, 17330): 2824.0177439864106, (55, 17334): 2821.6054381135486, (55, 17343): 2828.321301862207, (55, 17345): 2815.8255309685337, (55, 17347): 2819.922996563807, (55, 17351): 2811.8995951106886, (55, 17372): 2818.7215231657065, (55, 17373): 2828.743604136925, (55, 17377): 2828.995479825714, (55, 17382): 2821.3019873272897, (55, 17383): 2824.58095317948, (55, 17389): 2819.593373703747, (55, 17400): 2828.3315806979635, (55, 17401): 2829.0531531971087, (55, 17402): 2828.2548370746613, (55, 17403): 2828.5751383457973, (55, 17440): 2810.311700710109, (55, 17455): 2823.3299377200938, (55, 17491): 2819.9796239574534, (55, 17507): 2829.6805443406024, (55, 17509): 2835.5864965909545, (55, 17590): 2802.7433721109346, (55, 17615): 2813.014502320967, (55, 17642): 2814.7934625619, (55, 17643): 2812.291664747314, (55, 17668): 2814.1531226735387, (55, 17721): 2815.337973338514, (55, 17754): 2861.7082140281036, (55, 17769): 2837.443918818391, (55, 17776): 2809.3537689093414, (55, 17804): 2845.822438361912, (55, 17809): 2850.4225774641995, (55, 17824): 2850.9043715401444, (55, 17837): 2821.2728527398726, (55, 17838): 2818.6544160166995, (55, 17862): 2813.7572507204945, (55, 17866): 2824.9937694985088, (55, 17872): 2812.359422601126, (55, 17873): 2803.0808422555397, (55, 17881): 2816.8562678598873, (55, 17947): 1396.1922450947154, (55, 17951): 1394.271499172935, (55, 17953): 1397.5744612888782, (55, 17954): 1400.0966857932435, (55, 17959): 1389.4707648332574, (55, 17963): 1382.448149389268, (55, 18000): 1385.3816979164346, (55, 18001): 1390.2582636564011, (55, 18111): 1572.2052451239042, (55, 18148): 1583.9534825421345, (55, 18166): 1592.2264949032924, (55, 18189): 1566.304391328249, (55, 18239): 2833.1579197117926, (55, 18240): 2832.454290380581, (55, 18245): 2833.2496215019037, (55, 18247): 2831.5572895607706, (55, 18251): 2832.442147299003, (55, 18256): 2832.6445525962604, (55, 18258): 2831.12199992789, (55, 18259): 2830.9786806942275, (55, 18260): 2830.934545879656, (55, 18262): 2831.329277661748, (55, 18263): 2832.5754909854645, (55, 18264): 2832.5731930604024, (55, 18266): 2831.0904249889863, (55, 18267): 2831.179648668295, (55, 18268): 2830.980544639491, (55, 18269): 2831.0889007152546, (55, 18275): 2831.034858266848, (55, 18285): 2832.830354843088, (55, 18308): 2831.628013563378, (55, 18313): 2829.388931002989, (55, 18314): 2828.388719588169, (55, 18315): 2832.8821968861166, (55, 18316): 2831.980171414791, (55, 18317): 2831.975994809323, (55, 18320): 2833.234335342177, (55, 18321): 2832.838669482056, (55, 18322): 2833.0093602749766, (55, 18324): 2834.391905017236, (55, 18325): 2836.1341367894483, (55, 18326): 2835.5251108247467, (55, 18327): 2831.243314036537, (55, 18329): 2837.8902004988868, (55, 18330): 2834.307576826252, (55, 18331): 2833.5703993360526, (55, 18332): 2832.361188509177, (55, 18333): 2834.9010917038754, (55, 18336): 2835.226590934495, (55, 18337): 2836.3747015299336, (55, 18403): 2830.5953298350414, (55, 18432): 2781.6269017635927, (55, 18451): 2814.644578136553, (55, 18466): 2849.3113140619316, (55, 18481): 2835.640554215247, (55, 18483): 2835.0263794530824, (55, 18484): 2834.5377961936365, (55, 18485): 2833.687627317088, (55, 18486): 2838.4443057758276, (55, 18487): 2836.954488300395, (55, 18489): 2836.0998886317575, (55, 18490): 2839.990078309912, (55, 18491): 2841.04243101045, (55, 18492): 2834.1942245237815, (55, 18493): 2838.8011713818855, (55, 18494): 2835.1765253027957, (55, 18495): 2839.297847510379, (55, 18496): 2837.6922514320527, (55, 18497): 2837.177565375756, (55, 18498): 2835.198001841678, (55, 18499): 2836.6055867515765, (55, 18501): 2836.668889102966, (55, 18502): 2835.838377921831, (55, 18503): 2834.4556346259405, (55, 18504): 2837.3719948889575, (55, 18506): 2838.5632250050903, (55, 18507): 2838.1188534376997, (55, 18508): 2837.003746986829, (55, 18509): 2837.6027177880424, (55, 18510): 2835.3341604610096, (55, 18511): 2840.3229799065252, (55, 18512): 2838.0900559192764, (55, 18515): 2838.3277727867912, (55, 18516): 2840.412178736415, (55, 18517): 2840.2384477123746, (55, 18518): 2840.624951437102, (55, 18519): 2837.2152703930187, (55, 18520): 2836.00391242042, (55, 18522): 2839.926939678719, (55, 18523): 2840.807488705432, (55, 18532): 2843.0951651069436, (55, 18535): 2839.028861276607, (55, 18537): 2836.7657701871913, (55, 18539): 2837.587386435496, (55, 18540): 2838.219174989326, (55, 18541): 2839.6377219331857, (55, 18542): 2840.4749491426483, (55, 18543): 2836.5891142372066, (55, 18546): 2839.566733113043, (55, 18555): 2843.1777569672327, (55, 18556): 2844.288821944548, (55, 18565): 2843.729336113212, (55, 18567): 2846.0916506040344, (55, 18568): 2843.563498443478, (55, 18577): 2857.409254487122, (55, 18583): 2853.252257755276, (55, 18605): 2853.961560115895, (55, 18608): 2849.9463931446458, (55, 18616): 2867.0318971338297, (55, 18618): 2879.3343224093537, (55, 18625): 2870.6555596850435, (55, 18645): 2858.8611946970223, (55, 18646): 2863.0187659677877, (55, 18653): 2858.427525158192, (55, 18654): 2867.5438036342116, (55, 18655): 2862.550091273832, (55, 18666): 2890.420455185423, (55, 18837): 2779.733058699749, (55, 18974): 2799.120774364428, (55, 18999): 2800.1458018109256, (55, 19000): 2803.270537712263, (55, 19174): 2613.6168218543153, (55, 19342): 2663.3537606887085, (55, 19455): 2666.955765710209, (55, 19555): 2496.2496966370504, (55, 19564): 2489.0742103588336, (55, 19573): 2486.083836609073, (55, 19586): 2485.7970986523846, (55, 19605): 2490.7759898259833, (55, 19611): 2493.411182577853, (55, 19614): 2496.5989917463135, (55, 19641): 2560.672110028696, (55, 19702): 2554.519702584412, (55, 19713): 2550.846575372974, (55, 19731): 2495.4134629500877, (55, 19819): 2633.3635696807373, (55, 19893): 2680.5476238841484, (55, 19899): 2725.3388346218094, (55, 19929): 2689.8846250484935, (55, 19951): 2770.433696993106, (55, 19962): 2701.0766581670086, (55, 19970): 2709.3912599510145, (55, 19971): 2711.9333902009303, (55, 19972): 2706.7417348392228, (55, 19975): 2702.033027520572, (55, 19978): 2777.959519392964, (55, 19987): 2777.935016313995, (55, 19989): 2755.859506640081, (55, 20039): 2781.3128858158634, (55, 20043): 2788.5998528049463, (55, 20047): 2779.829018833386, (55, 20052): 2756.98397891011, (55, 20054): 2759.8283788760477, (55, 20085): 2857.5479247424473, (55, 20104): 2864.0251936207305, (55, 20132): 2826.2989454322965, (55, 20203): 2695.7620417027338, (55, 20280): 2692.9131988570466, (55, 20285): 2693.1866841569527, (55, 20290): 2695.5366804609816, (55, 20297): 2687.7023886852576, (55, 20309): 2798.0833563615374, (55, 20453): 2897.681668132355, (55, 20485): 2639.018851404338, (55, 20520): 2618.8763514043353, (55, 20526): 2618.2665463660733, (55, 20698): 1406.728023786197, (55, 20868): 1190.6006604914917, (55, 21042): 2358.0110584179756, (55, 21057): 2393.3493321938718, (55, 21066): 2380.047419789959, (55, 21075): 2367.562296555592, (55, 21093): 2366.3127488357254, (55, 21098): 2399.6725065882533, (55, 21127): 2363.9205851017787, (55, 21130): 2373.3632772545507, (55, 21144): 2367.036797692736, (55, 21146): 2361.579015638374, (55, 21147): 2364.849686989996, (55, 21148): 2372.886737286372, (55, 21153): 2337.391911561688, (55, 21293): 2424.249637818773, (55, 21426): 2364.203810967485, (55, 21442): 2393.2150793615183, (55, 21451): 2396.259955836397, (55, 21466): 2381.284780942935, (55, 21469): 2388.0707493017103, (55, 21471): 2377.7342899447713, (55, 21473): 2383.9590140015075, (55, 21475): 2379.072822464842, (55, 21482): 2390.307676707539, (55, 21484): 2389.9752478601076, (55, 21488): 2385.436398318593, (55, 21494): 2381.8852110790353, (55, 21498): 2386.2119997169248, (55, 21500): 2381.6187278374036, (55, 21514): 2404.557135459356, (55, 21537): 2386.663578915594, (55, 21662): 2417.52197578672, (55, 21691): 2393.434308831907, (55, 21757): 2329.10197754721, (55, 21777): 2307.1480824571186, (55, 21778): 2301.1896112303293, (55, 21779): 2307.178624454538, (55, 21790): 2310.9849317565763, (55, 21802): 2315.871049754073, (55, 21824): 2324.7038892203727, (55, 21874): 2311.9894911992524, (55, 21879): 2313.362066952904, (55, 21983): 2311.6750987681694, (55, 22002): 2394.1242058652942, (55, 22132): 2292.1500098617084, (55, 22261): 1783.3757276617948, (55, 22298): 1802.3648893655068, (55, 22339): 1795.7757820843021, (55, 22508): 1852.1189415425097, (55, 22841): 173.21185436915118, (55, 22842): 176.7211763530108, (55, 22874): 185.49342425602512, (55, 22941): 173.71881602002185, (55, 22956): 178.72138558019225, (55, 22960): 170.98731597196817, (55, 22968): 221.42625168387215, (55, 22970): 215.26580877432232, (55, 22974): 246.77660532520335, (55, 22980): 250.74029218556336, (55, 23025): 293.6106383117593, (55, 23028): 301.76224601564024, (55, 23081): 362.371431769147, (55, 23104): 430.84425703074925, (55, 23147): 292.30922622307605, (55, 23298): 2524.596625288312, (55, 23376): 2508.268705262108, (55, 23381): 2510.913591810467, (55, 23529): 2545.175498063716, (55, 23556): 2534.1291234038185, (55, 23718): 2504.245395841527, (55, 24001): 2619.3236070059147, (55, 24094): 2671.0035453485525, (55, 24129): 2687.505439129411, (55, 24174): 2661.677459095306, (55, 24235): 2703.949457561791, (55, 24259): 2714.2160658609596, (55, 24260): 2713.8765315249257, (55, 24261): 2709.518899574741, (55, 24305): 2730.82030907947, (55, 24306): 2735.1628103049557, (55, 24307): 2729.664975007454, (55, 24308): 2646.132562509042, (55, 24498): 2755.9074576539597, (55, 24499): 2756.678643615389, (55, 24500): 2753.1575294115487, (55, 24668): 2710.5615081015108, (55, 24711): 2786.2676216891437, (55, 24756): 2805.4338002348427, (55, 24788): 2806.9304934494553, (55, 24809): 2796.166508460407, (55, 24813): 2798.838143352664, (55, 24821): 2797.6446497835645, (55, 24825): 2799.893747854085, (55, 24832): 2794.3478376824464, (55, 24833): 2796.774015164394, (55, 24835): 2799.6054878311616, (55, 24837): 2802.495388174482, (55, 24840): 2794.472554125131, (55, 24841): 2797.1851672580565, (55, 24844): 2795.2610296674793, (55, 24845): 2794.822509010767, (55, 24846): 2798.3407056718047, (55, 24849): 2799.988788944722, (55, 24850): 2800.4068560137794, (55, 24863): 2761.8108465853097, (55, 24866): 2765.883543181274, (55, 24885): 2773.270124840623, (55, 24886): 2775.1165493896, (55, 24889): 2779.2786391151976, (55, 24903): 2780.605299926621, (55, 24909): 2761.3131105495686, (55, 24999): 2930.661812881394, (55, 25019): 2919.9012627695556, (55, 25028): 2929.4197494144114, (55, 25137): 2732.80242977196, (55, 25145): 2739.4281141509073, (55, 25208): 2838.840973006522, (55, 25233): 2830.4560439447355, (55, 25371): 2717.7511783602313, (55, 25377): 2693.8643212078596, (55, 25828): 2337.220042980889, (55, 25851): 2271.477744565006, (55, 25874): 2325.937456675626, (55, 25898): 2361.0694207813326, (55, 25946): 2331.025284915192, (55, 26047): 2465.7442216838813, (55, 26066): 2536.179824344064, (55, 26197): 2481.587541373315, (55, 26212): 2213.465215861637, (55, 26253): 2201.6044948969025, (55, 26254): 2204.756442765425, (55, 26257): 2213.257929192146, (55, 26258): 2205.244853772519, (55, 26260): 2209.0373842256195, (55, 26266): 2194.534375056219, (55, 26267): 2200.585010375408, (55, 26271): 2201.9717264962896, (55, 26304): 2240.3310937682527, (55, 26305): 2236.8066353834774, (55, 26363): 2335.2624109624358, (55, 26441): 1965.8012266111205, (55, 26442): 1963.449240519784, (55, 26450): 1967.7419320744978, (55, 26459): 1980.9202339311123, (55, 26462): 1986.0305006651492, (55, 26467): 1976.1684337676618, (55, 26471): 1972.3216440675044, (55, 26472): 1970.6941081329355, (55, 26473): 1968.9515480454404, (55, 26476): 1951.4747526362153, (55, 26485): 1972.7750142290026, (55, 26493): 1966.0322894081312, (55, 26524): 1990.280447456773, (55, 26525): 1987.143543055383, (55, 26556): 1974.2906261544117, (55, 26560): 1985.4434904113957, (55, 26561): 1990.0732441096075, (55, 26564): 1972.2585252629544, (55, 26569): 1987.0327297060367, (55, 26570): 1983.7794566625764, (55, 26573): 1977.4733452538205, (55, 26581): 1972.4383827246645, (55, 26583): 1976.3681694620295, (55, 26593): 1965.940774822589, (55, 26837): 1970.24570673578, (55, 26844): 1970.4650910735456, (55, 26863): 1957.428123895052, (55, 26893): 1952.6724699618837, (55, 26902): 1952.5093430165994, (55, 26905): 1964.0439643568254, (55, 26912): 1960.3303186651929, (55, 26921): 1955.9077252945333, (55, 26922): 1938.6506478916858, (55, 27212): 2225.9092812151525, (55, 27218): 2236.7450042390888, (55, 27239): 2223.84697509207, (55, 27257): 2219.8002340658663, (55, 27274): 2221.7039335723484, (55, 27279): 2217.3565039485375, (55, 27282): 2217.4543324813358, (55, 27283): 2225.741506016181, (55, 27285): 2219.1008729157934, (55, 27286): 2211.6734704332516, (55, 27290): 2216.855708169446, (55, 27295): 2223.3103031555434, (55, 27300): 2223.38993106815, (55, 27344): 2204.356331899915, (55, 27366): 2199.968761993981, (55, 27383): 2210.06978033062, (55, 27398): 2220.523037353628, (55, 27406): 2223.6944182801626, (55, 27407): 2227.1337486772463, (55, 27426): 2256.173411041858, (55, 27432): 2247.395978510793, (55, 27460): 2256.7355635325725, (55, 27523): 2132.664719084842, (55, 27545): 2210.155674541281, (55, 27602): 2187.4739100066995, (55, 27606): 2193.290946410715, (55, 27646): 2105.784627745478, (55, 27667): 2101.6914219343344, (55, 27672): 2104.8996581706215, (55, 27674): 2103.442733874338, (55, 27688): 2116.323178628836, (55, 27692): 2100.3324234459074, (55, 27693): 2100.193903957471, (55, 27705): 2096.3426138583345, (55, 27712): 2093.1239008357556, (55, 27786): 2326.461159047176, (55, 27790): 2371.5091555958284, (55, 27791): 2378.0765464726123, (55, 27795): 2321.6055250392774, (55, 27801): 2350.9684500884327, (55, 27813): 2321.5097457250768, (55, 27816): 2330.3744132942293, (55, 27823): 2352.494706264742, (55, 27830): 2340.5285597767947, (55, 27884): 2075.0629864703974, (55, 27885): 2101.6665625910523, (55, 27896): 2087.4087123118916, (55, 27919): 2090.0642131864797, (55, 27922): 2087.9336196186114, (55, 27930): 2083.695746200172, (55, 27934): 2081.4325394253374, (55, 27935): 2078.436416770175, (55, 27948): 2006.1471107602204, (55, 27951): 2065.750118260144, (55, 28061): 1600.724293741454, (55, 28290): 1631.849314559583, (55, 28292): 1615.0049967630405, (55, 28293): 1627.1803890489675, (55, 28295): 1615.8616719621632, (55, 28296): 1625.9005536758907, (55, 28297): 1639.559818846466, (55, 28302): 1629.3829499321898, (55, 28310): 819.0791322229862, (55, 28313): 798.7713886889927, (55, 28372): 830.6601028917132, (55, 28398): 827.8222745871184, (55, 28399): 827.14544007765, (55, 28400): 823.9185275502075, (55, 28401): 836.5421598756351, (55, 28445): 791.5944097786792, (55, 28475): 866.349448947318, (55, 28885): 2731.210243595186, (55, 28886): 2729.0207902783413, (55, 28915): 2736.099241957342, (55, 28916): 2731.9803461450547, (55, 28917): 2731.139757591168, (55, 28921): 2736.3337986815004, (55, 28931): 2736.5890235326183, (55, 28945): 2734.827730545693, (55, 28982): 2734.0246578279884, (55, 29219): 2775.514625354645, (55, 29228): 2759.604715682686, (55, 29246): 2874.0081505865137, (55, 29248): 2876.7457729030984, (55, 29282): 2853.8561655732633, (55, 29290): 2880.4356782258014, (55, 29291): 2877.200782473974, (55, 29292): 2880.832226789336, (55, 29293): 2872.0927117786773, (55, 29294): 2880.822627038257, (55, 29298): 2873.861782375455, (55, 29299): 2874.237937447235, (55, 29304): 2863.5923858096226, (55, 29317): 2841.1592966461003, (55, 29323): 2839.2901783092866, (55, 29330): 2850.292584898701, (55, 29331): 2854.815305598262, (55, 29344): 2785.8909301739877, (55, 29445): 2622.8108248891936, (55, 29724): 24.59993501855753, (55, 29738): 25.116811503804236, (55, 29745): 19.84570068854407, (55, 29748): 11.373422837660957, (55, 29750): 19.716274931510267, (55, 29759): 12.993758786889611, (55, 29772): 4.85567821508354, (55, 29781): 6.28076165709186, (55, 29784): 6.716131890734273, (55, 29790): 10.433410897603387, (55, 29811): 24.317161385980196, (55, 29817): 92.87243939433839, (55, 29818): 94.02857787807845, (55, 29929): 36.0724247585435, (55, 30039): 123.91048402417616, (55, 30066): 158.35620023947814, (55, 30116): 129.52012275422024, (55, 30238): 268.4512568941678, (55, 30248): 210.0347291336734, (55, 30260): 212.2271196656851, (55, 30545): 2664.3482592198925, (55, 30733): 2491.0348153198975, (55, 30756): 2476.1582388022434, (55, 30921): 2543.676906438483, (55, 31079): 1978.0704191256555, (55, 31149): 1989.5258711127685, (55, 31154): 1984.8971316332652, (55, 31160): 1989.1647699584364, (55, 31163): 1982.8531528671533, (55, 31189): 1940.4579336277375, (55, 31215): 1938.1988129021158, (55, 31259): 1908.9514502971892, (55, 31262): 1905.6870432038975, (55, 31430): 1968.6745629145046, (55, 31568): 1784.8604828529164, (55, 31751): 1938.5314526408704}
    
    # Precalculated costs for each active warehouse to each customer for both TL and LTL modes
    costs_TL = {(1, 109): 121.59487577764533, (1, 872): 279.5093430909297, (1, 873): 280.38347269615707, (1, 877): 280.0203043584775, (1, 879): 280.1465358533972, (1, 884): 279.18911944159424, (1, 889): 279.753776814514, (1, 891): 278.90943798120287, (1, 892): 280.83145238579465, (1, 894): 280.73554820301206, (1, 896): 279.9516814516257, (1, 903): 280.0127367484923, (1, 909): 278.639908171771, (1, 910): 279.022494558662, (1, 912): 278.43654021553925, (1, 913): 277.7789733376112, (1, 916): 277.54804761588696, (1, 926): 279.35190412322964, (1, 927): 279.0654825621708, (1, 948): 278.59833597365844, (1, 961): 279.24464995620065, (1, 962): 279.366597436638, (1, 963): 279.49631552686327, (1, 967): 280.39668280735975, (1, 974): 279.8447659434052, (1, 998): 280.71339432514105, (1, 1014): 300.24963642579047, (1, 1086): 278.24500158471903, (1, 1087): 278.23290677217125, (1, 1089): 277.37018144585153, (1, 1090): 277.732788240593, (1, 1092): 278.99999762702976, (1, 1097): 278.01394140605385, (1, 1107): 279.69313802502234, (1, 1387): 146.27541622432608, (1, 1554): 132.26869456410626, (1, 1827): 318.52982327915646, (1, 1828): 318.6433887336177, (1, 1829): 318.76308798025343, (1, 1830): 318.52632212187564, (1, 1831): 318.62220206487945, (1, 1832): 318.53779749947824, (1, 1833): 318.5652613782852, (1, 1836): 318.48366394013965, (1, 1841): 319.01806917560737, (1, 1843): 318.78376537027674, (1, 1844): 318.87128107157633, (1, 1845): 318.5775426570505, (1, 1847): 317.724108094052, (1, 1848): 318.0289883086993, (1, 1849): 319.4409772541998, (1, 1850): 319.60626215588053, (1, 1851): 318.2173435772275, (1, 1852): 318.2007172062952, (1, 1854): 318.3776213678842, (1, 1856): 317.62921976519897, (1, 1857): 317.9869072907874, (1, 1858): 319.32915981099603, (1, 1861): 318.71029833325287, (1, 1866): 317.575990702062, (1, 1867): 319.0671149569007, (1, 1868): 318.9107892457926, (1, 1870): 318.795079624089, (1, 1871): 319.0573470040244, (1, 1875): 318.38846688686823, (1, 1880): 317.855674070699, (1, 1882): 317.89052599915425, (1, 1883): 319.6625796682305, (1, 1889): 318.08103053466283, (1, 1893): 318.84319357216486, (1, 1894): 318.63520942403255, (1, 1899): 317.9144506241065, (1, 1900): 318.08898210774544, (1, 1902): 319.22311764589074, (1, 1905): 319.4802273737994, (1, 1907): 318.27847638771544, (1, 1910): 318.4304232981534, (1, 1917): 320.20067238856626, (1, 1920): 318.33376057628374, (1, 1935): 319.59307852331966, (1, 1937): 319.82115727069265, (1, 1946): 317.5144911001406, (1, 1949): 317.8045905989453, (1, 1950): 316.75766017514474, (1, 1951): 317.24187697585296, (1, 1952): 317.48655114667883, (1, 1953): 317.72726301936405, (1, 1954): 317.44411560212006, (1, 1958): 317.68655997388794, (1, 1960): 318.1223773000995, (1, 1968): 318.29457045757925, (1, 1969): 319.72254535797424, (1, 1974): 319.342534574885, (1, 1975): 319.31428833502935, (1, 1979): 318.705257606599, (1, 1980): 318.5805977531112, (1, 1981): 318.81871257038995, (1, 1985): 318.99727489264427, (1, 1994): 316.217252349806, (1, 2011): 317.85355088986205, (1, 2019): 320.0383597746701, (1, 2020): 319.74893472005186, (1, 2029): 318.5772734791331, (1, 2030): 319.5494881317684, (1, 2032): 318.3480649059749, (1, 2033): 319.0072480055457, (1, 2034): 318.95971516700763, (1, 2036): 317.6472880577961, (1, 2037): 317.9892417581368, (1, 2038): 318.26209166775106, (1, 2042): 321.71672750109667, (1, 2050): 318.90506033049775, (1, 2051): 318.8156364578518, (1, 2053): 318.92473349283347, (1, 2054): 319.22907976929173, (1, 2066): 318.6027656174889, (1, 2067): 318.624994057437, (1, 2071): 315.6593024554, (1, 2072): 316.26341042475, (1, 2073): 314.78127085933687, (1, 2074): 314.67906643458537, (1, 2080): 313.6448392020605, (1, 2082): 316.580556246857, (1, 2083): 316.8952673880758, (1, 2089): 316.28846069571716, (1, 2090): 316.58844822130374, (1, 2092): 316.2290100503822, (1, 2098): 314.0660514171985, (1, 2099): 314.3804702911647, (1, 2101): 313.972564559054, (1, 2102): 315.5931395879429, (1, 2103): 315.0702694312749, (1, 2104): 314.76881748240027, (1, 2106): 317.0825058013849, (1, 2112): 314.1575191536954, (1, 2113): 315.80368501186496, (1, 2114): 316.13753166325404, (1, 2117): 317.29627957378165, (1, 2123): 316.16542030104773, (1, 2124): 316.49967474801343, (1, 2134): 315.4725767629357, (1, 2138): 316.486011663542, (1, 2141): 315.6114536776626, (1, 2148): 315.80520387932825, (1, 2150): 314.7840969805224, (1, 2151): 315.114534644506, (1, 2152): 314.5794987301305, (1, 2153): 315.94663527264726, (1, 2154): 314.5807624248485, (1, 2155): 314.3706660396249, (1, 2156): 314.14936715542433, (1, 2157): 314.31389609465685, (1, 2160): 316.8127599524191, (1, 2161): 314.49291729475993, (1, 2162): 315.89052153676863, (1, 2163): 315.4312853908315, (1, 2164): 315.38140910601476, (1, 2168): 314.7689878615744, (1, 2172): 314.94446724980725, (1, 2174): 315.03743467313063, (1, 2178): 315.17816174401383, (1, 2179): 314.95058967003354, (1, 2183): 316.4296695523151, (1, 2185): 316.43278305931426, (1, 2186): 316.1755155000248, (1, 2190): 316.9103183510036, (1, 2192): 316.4409434276981, (1, 2193): 316.5333830890915, (1, 2194): 316.05370864839267, (1, 2195): 315.9459335602675, (1, 2197): 316.5247916594506, (1, 2205): 315.79888374938906, (1, 2207): 314.8662758342976, (1, 2208): 315.3801342516145, (1, 2212): 316.7571445795363, (1, 2214): 306.3759503092912, (1, 2225): 307.4187251830232, (1, 2231): 305.9675120901139, (1, 2278): 311.94948972041163, (1, 2284): 312.8708762128505, (1, 2285): 312.70339556557803, (1, 2291): 310.5404858388614, (1, 2292): 310.98844916342273, (1, 2307): 312.22050811270555, (1, 2313): 310.23373660115396, (1, 2317): 310.3488633674176, (1, 2319): 311.3067654810686, (1, 2321): 311.7235192337121, (1, 2323): 311.7289769799433, (1, 2326): 313.5832864670777, (1, 2327): 313.1544090835125, (1, 2329): 312.8549948854372, (1, 2330): 312.49860605522093, (1, 2332): 313.1745787683785, (1, 2344): 312.17420399886254, (1, 2346): 312.10903476857226, (1, 2361): 312.31364452794077, (1, 2368): 317.1054978081374, (1, 2374): 317.54275101859804, (1, 2375): 317.72312420411754, (1, 2377): 316.109403201521, (1, 2378): 318.00089370219655, (1, 2379): 317.9967948168425, (1, 2380): 318.1916308800585, (1, 2383): 316.5758541466019, (1, 2385): 316.8456310557628, (1, 2395): 316.9136824405008, (1, 2397): 317.78059096442, (1, 2398): 315.59027913186657, (1, 2399): 316.20239504304476, (1, 2400): 316.07073517140776, (1, 2402): 316.88247568736136, (1, 2403): 317.2463525509834, (1, 2404): 317.358869186008, (1, 2405): 316.4650446803743, (1, 2407): 317.22034626349864, (1, 2408): 317.6279988706187, (1, 2409): 316.7433222008899, (1, 2411): 317.167007956201, (1, 2412): 317.1003646223515, (1, 2413): 317.38832292274355, (1, 2414): 316.8925511878204, (1, 2422): 317.0292921864352, (1, 2424): 317.2199265290842, (1, 2426): 317.31438322686216, (1, 2433): 316.60539037851794, (1, 2436): 316.37430915363285, (1, 2437): 314.2608731312283, (1, 2440): 314.7403801825143, (1, 2445): 323.7196878254751, (1, 2447): 322.6098357055264, (1, 2454): 323.7003191144093, (1, 2455): 323.8006686733191, (1, 2460): 320.3614828804284, (1, 2461): 320.77727991340964, (1, 2471): 327.31267183830596, (1, 2492): 318.4379163113051, (1, 2511): 315.34385195033116, (1, 2523): 316.9206414114469, (1, 2525): 316.3105747070108, (1, 2535): 318.13232125846605, (1, 2537): 317.3526428380434, (1, 2538): 317.93538553687415, (1, 2539): 317.4931704542942, (1, 2540): 318.4803970094483, (1, 2542): 318.96738846412615, (1, 2559): 330.1944384886973, (1, 2575): 328.9563172357687, (1, 2599): 313.25628401540575, (1, 2600): 316.76537916221497, (1, 2607): 314.90087117333405, (1, 2627): 316.60184663175176, (1, 2647): 318.42564456865256, (1, 2674): 317.66667781666274, (1, 2681): 317.2627967271371, (1, 2683): 318.29133209734636, (1, 2686): 317.2379437145656, (1, 2689): 330.0785267809973, (1, 2690): 330.11037118672095, (1, 2713): 331.6746095974475, (1, 2714): 331.7630254040095, (1, 2715): 332.08827674319696, (1, 2739): 331.83798697921685, (1, 2740): 330.1453782939239, (1, 2741): 330.3323161729547, (1, 2749): 331.25244910644216, (1, 2750): 331.4000986597691, (1, 2752): 331.65280071330005, (1, 2755): 331.8807180102917, (1, 2758): 331.7669831975398, (1, 2759): 331.78881168947504, (1, 2769): 331.4638527861428, (1, 2771): 330.57700585719357, (1, 2779): 330.34563010672133, (1, 2784): 326.55078231126225, (1, 2800): 326.8718946332773, (1, 2802): 329.3409331383978, (1, 2803): 329.25888374605506, (1, 2804): 329.0586071812335, (1, 2805): 329.48902822294565, (1, 2807): 329.5107451218842, (1, 2809): 329.2964252752737, (1, 2812): 327.32314172897264, (1, 2814): 328.9079441855836, (1, 2817): 328.5990005053374, (1, 2819): 329.6554600070557, (1, 2823): 327.161790941921, (1, 2832): 329.83220845209263, (1, 2836): 328.3791017187043, (1, 2839): 329.5485630197117, (1, 2841): 328.8642345864249, (1, 2843): 328.8241598811306, (1, 2846): 328.4960154865501, (1, 2849): 329.9879717253877, (1, 2852): 329.68488921266345, (1, 2853): 330.12487181819984, (1, 2876): 330.07495002564974, (1, 2877): 331.2115024151448, (1, 2885): 331.159042084141, (1, 2918): 330.08565977420636, (1, 2921): 330.5377381012826, (1, 2925): 328.5453615611208, (1, 2926): 327.95239433249964, (1, 2930): 329.0760597437539, (1, 2931): 328.65041988919285, (1, 2938): 330.0204719392173, (1, 2940): 331.81064410555257, (1, 2947): 330.18822189818025, (1, 2949): 329.2230106048669, (1, 2950): 329.3780086186397, (1, 2952): 329.1288456522548, (1, 2958): 329.1095727480968, (1, 2959): 329.4288357712897, (1, 2960): 329.952148298991, (1, 2961): 329.65581053087317, (1, 2963): 328.85959015111143, (1, 2968): 328.97506019126416, (1, 2976): 328.8364389099336, (1, 2981): 323.62066156626497, (1, 2982): 323.4001235772694, (1, 2984): 323.1351281684929, (1, 3003): 322.61000636638204, (1, 3046): 320.3457577672619, (1, 3050): 322.4257751555309, (1, 3051): 322.651630853616, (1, 3053): 322.074838725472, (1, 3069): 324.9658731659865, (1, 3071): 322.1331259369889, (1, 3080): 331.0203094631404, (1, 3199): 321.2884031805148, (1, 3200): 320.65629865636737, (1, 3205): 324.24656436389955, (1, 3209): 320.9468619045056, (1, 3215): 320.7387091010367, (1, 3217): 320.0184041483032, (1, 3249): 320.8534220129179, (1, 3263): 326.31362607205864, (1, 3289): 322.70305240644103, (1, 3301): 322.7552877296823, (1, 3302): 322.54024153635896, (1, 3307): 322.22963877024614, (1, 3310): 323.06524148775276, (1, 3391): 321.3272532804027, (1, 3509): 210.26344025243975, (1, 3510): 209.76264224902, (1, 3511): 210.1591098125801, (1, 3512): 209.90435421612386, (1, 3514): 210.05934012334032, (1, 3519): 211.12964818211816, (1, 3536): 211.25771142528524, (1, 3545): 212.10715208276181, (1, 3548): 211.42068497629944, (1, 3572): 211.4659496213614, (1, 3581): 210.6490521827636, (1, 3583): 210.567133895443, (1, 3601): 211.97262078727036, (1, 3656): 210.9163243747, (1, 3669): 209.4082443444062, (1, 3670): 209.83496525306842, (1, 3695): 207.4906988222271, (1, 3696): 207.8547730727831, (1, 3782): 212.6680632417833, (1, 3792): 211.9570572994997, (1, 3989): 12.5, (1, 4008): 12.5, (1, 4031): 12.5, (1, 4045): 12.5, (1, 4144): 12.5, (1, 4145): 13.525909285617937, (1, 4164): 12.5, (1, 4168): 13.04490892885698, (1, 4173): 13.454408954541764, (1, 4181): 13.39184822092256, (1, 4228): 12.5, (1, 4248): 14.388718483387317, (1, 4254): 30.463144474372893, (1, 4260): 29.5969888178049, (1, 4262): 29.465301013331388, (1, 4273): 29.07365074166151, (1, 4319): 40.15129373597679, (1, 4326): 40.21504185045403, (1, 4328): 39.89971487242171, (1, 4334): 40.06011572482741, (1, 4335): 40.38498551171058, (1, 4372): 125.72373454630944, (1, 4413): 131.02984627275163, (1, 4434): 124.986598459644, (1, 4447): 123.47048718560174, (1, 4452): 125.32320059112939, (1, 4463): 132.7644509295581, (1, 4465): 132.15160908716854, (1, 4619): 137.35223119258617, (1, 4645): 136.6264531035938, (1, 4657): 137.34023977723996, (1, 4666): 137.92838702228968, (1, 4676): 138.04978935494114, (1, 4678): 137.72600212016337, (1, 4689): 138.5229760659718, (1, 4704): 139.4017657000344, (1, 4726): 158.2337615812166, (1, 4727): 157.94537652344215, (1, 4730): 157.3384217466663, (1, 4731): 157.83216740323437, (1, 4734): 156.31686564157988, (1, 4735): 156.31984962373684, (1, 4736): 156.69698198482158, (1, 4737): 156.538979951475, (1, 4738): 156.7969058172128, (1, 4756): 157.2313139810495, (1, 4760): 154.4416351265408, (1, 4761): 154.06055507896895, (1, 4762): 154.38018364831603, (1, 4765): 154.74484743022063, (1, 4773): 158.5354579542841, (1, 4774): 158.71811152233172, (1, 4790): 158.27760348780106, (1, 4795): 157.9152651102957, (1, 4799): 159.0757020910079, (1, 4801): 160.28089832809533, (1, 4804): 157.4616873876526, (1, 4805): 157.17033074468557, (1, 4806): 159.2569413541837, (1, 4815): 159.3676170456705, (1, 4816): 159.8892190590409, (1, 4817): 160.53688046688163, (1, 4826): 159.95190908629306, (1, 4830): 159.7588528515348, (1, 4839): 155.3012180790826, (1, 4840): 155.77625699798446, (1, 4841): 155.35050388682274, (1, 4846): 155.06588424036397, (1, 4848): 155.44209358009886, (1, 4850): 155.77690369537012, (1, 4871): 150.45490567719534, (1, 4883): 153.47622254078533, (1, 4900): 151.2955467048952, (1, 4901): 151.2973623977822, (1, 4917): 145.96733664139194, (1, 4931): 144.70484063986638, (1, 4944): 145.7856418310263, (1, 4956): 145.26007300964667, (1, 4958): 145.86823625560962, (1, 4959): 146.07248939236234, (1, 4961): 145.2508863756911, (1, 4966): 145.32857861562465, (1, 5207): 144.03622721263426, (1, 5272): 106.29835985620961, (1, 5283): 106.65976601410189, (1, 5287): 108.80249656876443, (1, 5289): 109.02831557076075, (1, 5293): 104.84861332939289, (1, 5295): 105.65208554352996, (1, 5296): 106.59412579770186, (1, 5298): 107.11261720012375, (1, 5303): 108.17483529591175, (1, 5305): 107.96607296270913, (1, 5306): 109.0827125672919, (1, 5307): 107.90011437048234, (1, 5308): 108.40511165395044, (1, 5313): 107.2022236166752, (1, 5314): 107.02646840550052, (1, 5317): 109.02297803782453, (1, 5319): 108.1098397824583, (1, 5324): 107.21664462574977, (1, 5326): 106.58843446902307, (1, 5348): 109.82830060173133, (1, 5351): 111.35862406581691, (1, 5399): 110.5871837025038, (1, 5413): 113.81994897806585, (1, 5422): 109.81319776384144, (1, 5445): 109.54777023956194, (1, 5448): 109.289078977632, (1, 5456): 110.2292799647951, (1, 5467): 110.73593229901134, (1, 5624): 105.13222388113876, (1, 5671): 101.34958942265214, (1, 5672): 100.6974677790747, (1, 5797): 109.23211564148639, (1, 5871): 124.07503076540162, (1, 5976): 120.59269400318696, (1, 6118): 266.64224700777277, (1, 6248): 275.97750034742836, (1, 6345): 94.19295758408515, (1, 6352): 96.3705057554556, (1, 6354): 93.72169234205222, (1, 6359): 93.1934139845616, (1, 6376): 95.8036032656557, (1, 6378): 93.965690370334, (1, 6381): 93.30015117185714, (1, 6383): 94.69226580227144, (1, 6396): 93.17486914001437, (1, 6399): 94.04714829229148, (1, 6408): 96.38507664699546, (1, 6409): 95.62999847590267, (1, 6419): 99.5373209871799, (1, 6422): 96.30361340415516, (1, 6423): 96.49302310358497, (1, 6424): 94.2467154908032, (1, 6439): 94.7492220451918, (1, 6464): 95.4305679471638, (1, 6465): 95.54648476556241, (1, 6469): 95.0778837688297, (1, 6470): 95.16503652165295, (1, 6472): 92.42283157049725, (1, 6480): 93.33856825386216, (1, 6486): 92.64425144103171, (1, 6497): 92.89247158353608, (1, 6503): 95.89568638403583, (1, 6508): 95.41132552432042, (1, 6509): 95.15509382410178, (1, 6521): 93.29817113529509, (1, 6544): 93.76822597540924, (1, 6552): 96.43009784550948, (1, 6553): 96.79258275014782, (1, 6554): 97.15747782347317, (1, 6578): 95.78026898491913, (1, 6582): 96.36603308642621, (1, 6601): 95.68235777761586, (1, 6609): 92.50864649761101, (1, 6610): 92.47448103734968, (1, 6611): 92.23520328159914, (1, 6614): 92.32139177619746, (1, 6615): 92.31293056373822, (1, 6616): 92.16484192244387, (1, 6617): 92.24709720372778, (1, 6618): 91.9603314006147, (1, 6619): 92.61113630913763, (1, 6620): 92.2666315453104, (1, 6621): 92.58761923992448, (1, 6622): 92.4417632933105, (1, 6623): 92.46469936497417, (1, 6624): 92.84109586782884, (1, 6625): 92.84114788674917, (1, 6626): 92.58423385779712, (1, 6627): 92.30883467301356, (1, 6628): 92.44238993297729, (1, 6629): 92.88905022664856, (1, 6630): 92.9375708154349, (1, 6632): 92.85989549768183, (1, 6634): 93.32710402831911, (1, 6635): 92.63572380276787, (1, 6636): 92.18561901170717, (1, 6637): 93.31189609020484, (1, 6638): 92.99619281711149, (1, 6639): 92.33531647160751, (1, 6640): 92.89447536633939, (1, 6641): 92.68255094707104, (1, 6642): 93.05736426667954, (1, 6643): 92.54818857637167, (1, 6645): 92.61505676698773, (1, 6646): 91.97997616747027, (1, 6647): 92.9287150798644, (1, 6653): 92.29526335962363, (1, 6655): 92.29964241122462, (1, 6658): 93.38871571639292, (1, 6662): 93.14912221793739, (1, 6819): 111.71225350737714, (1, 6996): 107.75689854392117, (1, 7059): 103.7966621925874, (1, 7187): 116.189510295364, (1, 7304): 120.96475421462115, (1, 7528): 110.3067255629966, (1, 7720): 85.63841083005593, (1, 7793): 87.20781531410194, (1, 7807): 86.53616121253432, (1, 7808): 87.58426848241007, (1, 7831): 91.1341649536073, (1, 7850): 86.71533148941353, (1, 7852): 87.42608806449634, (1, 8012): 85.27275840173169, (1, 8125): 90.96353936288396, (1, 8208): 79.14996906883911, (1, 8392): 90.60505462316858, (1, 8651): 131.6051371274161, (1, 9088): 111.57279016020954, (1, 9443): 146.86807047553336, (1, 9444): 146.42213020457055, (1, 9828): 167.54980251728065, (1, 9868): 165.06008165963738, (1, 10180): 91.37694825650327, (1, 10256): 84.37673273794756, (1, 10276): 86.09731267565148, (1, 10378): 80.81783653580804, (1, 10676): 100.8410857601141, (1, 10714): 107.68149890202167, (1, 10730): 101.74196630077228, (1, 10862): 163.7590927175472, (1, 10881): 163.5176891287918, (1, 10883): 163.80477611282947, (1, 10885): 163.74731208212097, (1, 10891): 164.2575940719717, (1, 10909): 163.65745411082918, (1, 10911): 162.9858266518497, (1, 10913): 163.24749425227859, (1, 10915): 162.92131073591145, (1, 10919): 162.6113233615127, (1, 11037): 172.17158147506692, (1, 11039): 170.23702689839297, (1, 11516): 37.553423014322284, (1, 11856): 39.963577591981114, (1, 11857): 41.27190945648806, (1, 11861): 40.636563216903845, (1, 11881): 39.37329892003806, (1, 11902): 40.18566698694897, (1, 11911): 39.28102546208905, (1, 11914): 39.62059035001064, (1, 11922): 39.372839788178545, (1, 11924): 38.9038441686944, (1, 11926): 39.071823414331625, (1, 11950): 37.41711531079073, (1, 11963): 36.86507117282282, (1, 11983): 35.379545130254314, (1, 11985): 36.72068108464876, (1, 12009): 35.13451151500825, (1, 12010): 35.94737963114746, (1, 12018): 35.654216060774516, (1, 12020): 35.78137515301988, (1, 12021): 35.530183323590464, (1, 12024): 35.15877010368806, (1, 12025): 35.6263594133567, (1, 12027): 35.62698840393283, (1, 12031): 36.029184327808025, (1, 12032): 36.14955847046677, (1, 12035): 34.77364915517091, (1, 12041): 37.69080965528063, (1, 12045): 43.904875270485, (1, 12145): 38.00507907802317, (1, 12275): 12.5, (1, 12294): 12.5, (1, 12358): 13.21385111796665, (1, 12463): 17.037033978841396, (1, 12465): 16.93194719737091, (1, 12482): 18.600593254317218, (1, 12503): 18.345976520184553, (1, 12506): 18.805416905800467, (1, 12549): 18.006082192544316, (1, 12559): 17.5878142196311, (1, 12569): 17.8882550476747, (1, 12572): 18.240859161405, (1, 12574): 17.524632759358642, (1, 12576): 18.456868834602005, (1, 12591): 18.637052201552567, (1, 12608): 21.76052582744446, (1, 12696): 17.429052962981824, (1, 12710): 20.755365047905148, (1, 12728): 18.7635942956071, (1, 12766): 57.36641449672896, (1, 12771): 60.62098121352293, (1, 12790): 61.07799775858045, (1, 12795): 62.1344855869608, (1, 12797): 66.5609138666947, (1, 12798): 65.96310979658642, (1, 12811): 62.44510439750006, (1, 12830): 63.60331655700873, (1, 12848): 63.04275401493759, (1, 12850): 62.799952543642945, (1, 12852): 63.781573686132184, (1, 12854): 64.32058403051458, (1, 12859): 62.52730658410242, (1, 12861): 65.38032064264775, (1, 12865): 61.766448194422665, (1, 12866): 62.05409163751462, (1, 12867): 60.96567319320911, (1, 12874): 61.49162217210805, (1, 12875): 61.08857238378462, (1, 12881): 62.74875294951229, (1, 12883): 62.083731013446446, (1, 12885): 60.73237181085094, (1, 12888): 62.39856556091441, (1, 12889): 62.55695530194442, (1, 12892): 61.372592255760125, (1, 12893): 62.367668362330825, (1, 12896): 62.05318198141913, (1, 12906): 61.44344787344857, (1, 13018): 66.80839010031094, (1, 13071): 67.02457890557865, (1, 13131): 70.57679826526763, (1, 13146): 67.01426140498684, (1, 13159): 72.6446787124969, (1, 13193): 71.24887432827721, (1, 13198): 77.47718677672138, (1, 13292): 70.381796730782, (1, 13296): 68.59705120370326, (1, 13406): 81.33395426423111, (1, 13407): 81.55052539354112, (1, 13417): 82.20242205686314, (1, 13418): 81.57961275089262, (1, 13438): 78.69222239826293, (1, 13442): 78.1031515996225, (1, 13443): 78.63055106662924, (1, 13764): 126.9238672909715, (1, 13766): 126.24273209484541, (1, 13771): 127.14543205285337, (1, 13783): 127.11881831429292, (1, 13784): 125.4003100421147, (1, 13792): 128.83477841040346, (1, 13824): 127.62956350828648, (1, 14017): 122.53929532179187, (1, 14870): 150.57212453219987, (1, 14997): 119.48201787150205, (1, 15000): 119.62252337054787, (1, 15003): 119.4227734465659, (1, 15006): 117.63092027728659, (1, 15007): 117.24093204717883, (1, 15056): 117.89787500353005, (1, 15063): 118.38245105876554, (1, 15069): 118.75436804434943, (1, 15076): 117.31688548056948, (1, 15086): 118.35425875233578, (1, 15087): 119.06993430452972, (1, 15111): 120.11266350348828, (1, 15116): 119.53230439033756, (1, 15722): 130.3979724314565, (1, 15998): 142.79171198655305, (1, 16073): 223.65309084267253, (1, 16939): 289.2729521214038, (1, 16940): 288.64032699645605, (1, 16951): 289.21309071997365, (1, 16963): 289.31040776645733, (1, 16965): 290.14518816692276, (1, 16969): 289.86546782076556, (1, 16970): 289.6412745664239, (1, 16971): 288.89454142976325, (1, 16973): 288.79133376721916, (1, 16974): 290.42990449201693, (1, 16976): 289.7326737023073, (1, 16978): 289.2056730403497, (1, 16980): 290.0535953147286, (1, 16982): 290.3686281323783, (1, 17045): 308.31882609411093, (1, 17048): 309.24829761890584, (1, 17304): 17.997172442317627, (1, 17305): 16.815887157464505, (1, 17330): 17.12749521169148, (1, 17334): 18.395217955258378, (1, 17343): 16.76452909572818, (1, 17345): 17.08340788315936, (1, 17347): 16.274538266910756, (1, 17351): 18.69424347303816, (1, 17372): 17.917158954422387, (1, 17373): 16.975953766566505, (1, 17377): 16.80514436888904, (1, 17382): 17.119100977746374, (1, 17383): 17.501355917451995, (1, 17389): 17.597818827901378, (1, 17400): 17.477376303804792, (1, 17401): 17.695290005884974, (1, 17402): 17.330820251487726, (1, 17403): 17.192968666259482, (1, 17440): 15.64246286327811, (1, 17455): 15.937233563868993, (1, 17491): 14.927481849189553, (1, 17507): 21.67944625615178, (1, 17509): 21.882775066740177, (1, 17590): 17.386745536536655, (1, 17615): 26.84065202114482, (1, 17642): 25.979067338627996, (1, 17643): 25.495957433794707, (1, 17668): 27.16357835385078, (1, 17721): 30.48903885009006, (1, 17754): 29.857455439458697, (1, 17769): 23.162756219808422, (1, 17776): 21.393601721579312, (1, 17804): 23.222005154290983, (1, 17809): 23.135163271684753, (1, 17824): 24.052038496252894, (1, 17837): 20.407635228534694, (1, 17838): 19.646635691339025, (1, 17862): 19.412881074575512, (1, 17866): 19.447739523842433, (1, 17872): 19.982973708262417, (1, 17873): 19.864147729492835, (1, 17881): 19.958604443649513, (1, 17947): 238.153375048129, (1, 17951): 236.85384672209435, (1, 17953): 236.63722732031835, (1, 17954): 236.7488355587603, (1, 17959): 237.831986014236, (1, 17963): 237.3185126063354, (1, 18000): 230.7963237317385, (1, 18001): 231.09975028324507, (1, 18111): 250.67130345748652, (1, 18148): 218.29380004500902, (1, 18166): 231.00310602076564, (1, 18189): 242.48815160872405, (1, 18239): 17.43657883171763, (1, 18240): 17.28687800744609, (1, 18245): 17.350601515632064, (1, 18247): 17.209140851733306, (1, 18251): 17.167442447706136, (1, 18256): 16.947503044077493, (1, 18258): 16.88179184217177, (1, 18259): 16.796768091650904, (1, 18260): 16.674953883641106, (1, 18262): 16.55462284077655, (1, 18263): 16.856258321339237, (1, 18264): 16.745125674941303, (1, 18266): 16.41440908778275, (1, 18267): 16.326976459306323, (1, 18268): 16.2277748462685, (1, 18269): 16.03799561005337, (1, 18275): 16.126784187592346, (1, 18285): 16.84238919062443, (1, 18308): 18.860106246580287, (1, 18313): 19.13111674703705, (1, 18314): 18.53891854927447, (1, 18315): 16.464564463844525, (1, 18316): 16.273246217773735, (1, 18317): 16.171937694295238, (1, 18320): 16.369292522391554, (1, 18321): 16.222489017716537, (1, 18322): 16.10451495602941, (1, 18324): 16.297151981122816, (1, 18325): 16.214733247193607, (1, 18326): 16.254318220870942, (1, 18327): 15.910492192632368, (1, 18329): 16.405457992790534, (1, 18330): 15.815149359802726, (1, 18331): 15.969822502206691, (1, 18332): 16.026466374132042, (1, 18333): 16.003575165625914, (1, 18336): 16.352482122529572, (1, 18337): 16.453793110684867, (1, 18403): 15.36020552390559, (1, 18432): 12.5, (1, 18451): 13.87897506329929, (1, 18466): 17.512335731054144, (1, 18481): 16.977969177124194, (1, 18483): 16.83485383022988, (1, 18484): 16.992611436301992, (1, 18485): 17.618217033560548, (1, 18486): 17.99732748031123, (1, 18487): 18.286054174148234, (1, 18489): 17.52323011009588, (1, 18490): 17.803955500954178, (1, 18491): 17.754598086108857, (1, 18492): 18.285188732168756, (1, 18493): 18.188032929654153, (1, 18494): 17.428663373875555, (1, 18495): 17.863175177737425, (1, 18496): 17.798979522188258, (1, 18497): 18.48649479388689, (1, 18498): 17.873631423047907, (1, 18499): 17.73515445278173, (1, 18501): 18.08940636639777, (1, 18502): 18.195280238082628, (1, 18503): 18.10213363390095, (1, 18504): 17.59975711149624, (1, 18506): 18.490790569285497, (1, 18507): 18.67337310349927, (1, 18508): 17.89398227415417, (1, 18509): 18.02896111858734, (1, 18510): 18.300846752719828, (1, 18511): 18.456923537987386, (1, 18512): 18.284124807172816, (1, 18515): 17.79638610343065, (1, 18516): 18.26453513171209, (1, 18517): 18.601697162384923, (1, 18518): 18.068628193600155, (1, 18519): 17.498461766567996, (1, 18520): 17.74750006324769, (1, 18522): 16.880834959810148, (1, 18523): 17.024662878999738, (1, 18532): 17.158506754140316, (1, 18535): 17.045384190351594, (1, 18537): 16.98768757398798, (1, 18539): 17.081526132747236, (1, 18540): 17.175004247104873, (1, 18541): 17.275563305813392, (1, 18542): 17.324945643970782, (1, 18543): 17.147819837102723, (1, 18546): 17.498124721294026, (1, 18555): 17.608134646590216, (1, 18556): 17.736788773139832, (1, 18565): 17.36335060628905, (1, 18567): 17.70856763805599, (1, 18568): 17.511071662359132, (1, 18577): 17.963875562952037, (1, 18583): 17.442811829816623, (1, 18605): 17.02668801630435, (1, 18608): 18.378796627807677, (1, 18616): 17.60134280069753, (1, 18618): 18.447674986495862, (1, 18625): 17.099018112759676, (1, 18645): 16.14656972120032, (1, 18646): 16.64424779863431, (1, 18653): 17.335192867154845, (1, 18654): 17.776368364717413, (1, 18655): 17.71819466508004, (1, 18666): 17.770014610206655, (1, 18837): 12.5, (1, 18974): 12.5, (1, 18999): 12.5, (1, 19000): 12.5, (1, 19174): 18.644399312780354, (1, 19342): 12.5, (1, 19455): 16.0664432423651, (1, 19555): 33.50293071324449, (1, 19564): 32.83466602779032, (1, 19573): 33.48104216871353, (1, 19586): 33.74702633274245, (1, 19605): 33.38740509246726, (1, 19611): 32.905353731640595, (1, 19614): 33.02796401774738, (1, 19641): 24.502878413105087, (1, 19702): 24.900114939635053, (1, 19713): 25.44544629624664, (1, 19731): 36.76641599614149, (1, 19819): 18.235584035655208, (1, 19893): 73.52173147860319, (1, 19899): 75.61463451898969, (1, 19929): 73.18038276235089, (1, 19951): 74.65286609912727, (1, 19962): 74.8839367217433, (1, 19970): 71.79328859741723, (1, 19971): 72.57007372897729, (1, 19972): 73.04239080135379, (1, 19975): 72.46451357087169, (1, 19978): 71.45550011027133, (1, 19987): 70.9492680504587, (1, 19989): 70.46538320982906, (1, 20039): 70.78477037534464, (1, 20043): 70.266050830098, (1, 20047): 69.43048710739272, (1, 20052): 69.50046095814974, (1, 20054): 69.88774186573882, (1, 20085): 67.97619490812095, (1, 20104): 68.06079282045218, (1, 20132): 68.4315646604853, (1, 20203): 80.48907703766913, (1, 20280): 82.67761157999233, (1, 20285): 83.60907391664938, (1, 20290): 82.26440848002197, (1, 20297): 82.04176115619275, (1, 20309): 77.27912284988047, (1, 20453): 75.23149965562216, (1, 20485): 81.11662112974479, (1, 20520): 80.68377216537341, (1, 20526): 82.94861713874646, (1, 20698): 150.94493500385286, (1, 20868): 175.1718518534331, (1, 21042): 67.33952952398343, (1, 21057): 62.62665325095926, (1, 21066): 65.38708155193028, (1, 21075): 65.62582123759981, (1, 21093): 67.6082373610819, (1, 21098): 65.28524930163954, (1, 21127): 67.27961773117853, (1, 21130): 66.70691305523238, (1, 21144): 66.24519676202057, (1, 21146): 67.58306798825397, (1, 21147): 66.15115474035947, (1, 21148): 65.54002822258595, (1, 21153): 65.44756422109187, (1, 21293): 60.461022574832164, (1, 21426): 56.85127601972637, (1, 21442): 51.184189435192884, (1, 21451): 50.6548772016958, (1, 21466): 54.18027599653824, (1, 21469): 53.48883857880033, (1, 21471): 54.525231691203984, (1, 21473): 53.99035091052495, (1, 21475): 54.50987010733036, (1, 21482): 52.925739119319424, (1, 21484): 53.13607250200435, (1, 21488): 53.507833963687055, (1, 21494): 54.692982675071896, (1, 21498): 54.133669219961185, (1, 21500): 55.16718561540793, (1, 21514): 54.51358228715604, (1, 21537): 55.77460241915883, (1, 21662): 54.54030444630941, (1, 21691): 57.30928874677808, (1, 21757): 60.80468424326273, (1, 21777): 78.28084964618391, (1, 21778): 78.9511068777399, (1, 21779): 78.8878607678989, (1, 21790): 77.19271218943001, (1, 21802): 77.83903263696662, (1, 21824): 77.46942576747473, (1, 21874): 79.10583420750376, (1, 21879): 80.09454379890171, (1, 21983): 74.16067707126518, (1, 22002): 69.15575866778423, (1, 22132): 67.5688694514521, (1, 22261): 178.00912634170413, (1, 22298): 176.85776144535586, (1, 22339): 186.49894199705128, (1, 22508): 163.35354823558038, (1, 22841): 312.2359868535552, (1, 22842): 312.315020539706, (1, 22874): 310.7770822436117, (1, 22941): 310.7048938395932, (1, 22956): 311.866780737252, (1, 22960): 312.0094074749713, (1, 22968): 314.10995474904206, (1, 22970): 314.2662358696343, (1, 22974): 315.43606201660543, (1, 22980): 316.76217527744626, (1, 23025): 317.5118835628118, (1, 23028): 317.395350716639, (1, 23081): 320.68611564455813, (1, 23104): 319.7025785897519, (1, 23147): 305.6039906485681, (1, 23298): 44.135782674698014, (1, 23376): 46.16765024327788, (1, 23381): 49.00382578717401, (1, 23529): 44.25061875949454, (1, 23556): 45.16664510238543, (1, 23718): 44.15981332359752, (1, 24001): 32.04818134782152, (1, 24094): 32.488676800541896, (1, 24129): 30.869237463675383, (1, 24174): 35.94762897031754, (1, 24235): 33.698644174639, (1, 24259): 31.075047562109994, (1, 24260): 31.36897648879113, (1, 24261): 31.495013348285713, (1, 24305): 28.963330219067828, (1, 24306): 28.97403525872275, (1, 24307): 29.20543498242128, (1, 24308): 25.17362345260377, (1, 24498): 21.719499502942547, (1, 24499): 21.790935330474255, (1, 24500): 21.91160219153732, (1, 24668): 19.047301734362616, (1, 24711): 22.73354005765447, (1, 24756): 24.193112991201787, (1, 24788): 23.133587234568775, (1, 24809): 25.99941850957327, (1, 24813): 24.924685629140267, (1, 24821): 25.19949993888684, (1, 24825): 25.331544236489787, (1, 24832): 25.930715804825123, (1, 24833): 25.678083844834564, (1, 24835): 25.531537741180365, (1, 24837): 24.902661804133466, (1, 24840): 26.091682202655054, (1, 24841): 25.449471275862805, (1, 24844): 26.244981101679443, (1, 24845): 25.370258200772167, (1, 24846): 26.30102389676049, (1, 24849): 26.24531470023383, (1, 24850): 25.052196350184143, (1, 24863): 27.648865853409017, (1, 24866): 27.0739243739726, (1, 24885): 26.993957522327964, (1, 24886): 27.293730090068657, (1, 24889): 24.971311030523324, (1, 24903): 24.010609036137286, (1, 24909): 25.04920389023546, (1, 24999): 17.116987036468174, (1, 25019): 15.977362370579772, (1, 25028): 16.96854225002222, (1, 25137): 92.1091105891661, (1, 25145): 91.74634643803908, (1, 25208): 97.0248320118355, (1, 25233): 97.64232612722203, (1, 25371): 86.44076104880905, (1, 25377): 85.79436178464266, (1, 25828): 107.03128426610853, (1, 25851): 108.76009568162375, (1, 25874): 105.34828407588512, (1, 25898): 106.25978194301437, (1, 25946): 107.29827617573224, (1, 26047): 104.71705057556449, (1, 26066): 81.66746911717117, (1, 26197): 94.20537172671155, (1, 26212): 130.07837729624265, (1, 26253): 132.3998412706892, (1, 26254): 131.33314293780495, (1, 26257): 131.1058885733753, (1, 26258): 132.10223226302458, (1, 26260): 131.54589091283282, (1, 26266): 131.10922857831116, (1, 26267): 130.65093086518416, (1, 26271): 130.79100084618898, (1, 26304): 122.04213280704725, (1, 26305): 121.68544328759853, (1, 26363): 111.73960380244048, (1, 26441): 184.60213182225175, (1, 26442): 184.34393115160174, (1, 26450): 183.1601905164905, (1, 26459): 183.12909077823443, (1, 26462): 183.32166079948206, (1, 26467): 186.80597714323275, (1, 26471): 185.79843175579578, (1, 26472): 185.68592316237576, (1, 26473): 185.637067764869, (1, 26476): 184.98865994687895, (1, 26485): 183.68989331481123, (1, 26493): 183.69442660111267, (1, 26524): 183.87138474635424, (1, 26525): 183.71814100716782, (1, 26556): 185.330187376342, (1, 26560): 185.26560042085993, (1, 26561): 184.5241636893355, (1, 26564): 184.99480830446814, (1, 26569): 184.3243212688039, (1, 26570): 184.00552185943607, (1, 26573): 184.17137762481494, (1, 26581): 184.1220660491009, (1, 26583): 183.8754726824163, (1, 26593): 184.10273224118495, (1, 26837): 187.02025356683424, (1, 26844): 187.82629313960462, (1, 26863): 186.0185256932256, (1, 26893): 188.31703258750375, (1, 26902): 189.40991507700787, (1, 26905): 188.35053559673386, (1, 26912): 189.1887223582665, (1, 26921): 187.12279083245585, (1, 26922): 184.8566650642183, (1, 27212): 193.2240133773013, (1, 27218): 192.2684981743066, (1, 27239): 194.76942473088494, (1, 27257): 193.95676623602853, (1, 27274): 195.0801360796497, (1, 27279): 194.89958903651595, (1, 27282): 193.98796619855892, (1, 27283): 194.3631728856006, (1, 27285): 195.48819934998656, (1, 27286): 194.6386513664273, (1, 27290): 193.20737446181045, (1, 27295): 192.657525495458, (1, 27300): 195.2404578823206, (1, 27344): 192.76312381290552, (1, 27366): 193.7868097784939, (1, 27383): 195.55067759636347, (1, 27398): 196.6825637302447, (1, 27406): 195.78165836875343, (1, 27407): 196.05709411209287, (1, 27426): 194.9099239494243, (1, 27432): 190.951389432414, (1, 27460): 193.43712540018254, (1, 27523): 193.9412472230558, (1, 27545): 210.27132163586467, (1, 27602): 230.9279208092066, (1, 27606): 231.31473097020773, (1, 27646): 209.5312753341817, (1, 27667): 213.664677317932, (1, 27672): 213.88870824200794, (1, 27674): 213.17965664710786, (1, 27688): 213.79791052788525, (1, 27692): 214.59515783776612, (1, 27693): 213.97495968804307, (1, 27705): 213.9340189428383, (1, 27712): 214.23174760468459, (1, 27786): 231.86507120964245, (1, 27790): 229.4609457450189, (1, 27791): 229.25243033715176, (1, 27795): 230.70338699633737, (1, 27801): 228.92223543102887, (1, 27813): 232.51091860799303, (1, 27816): 231.7432013784038, (1, 27823): 228.85391280198738, (1, 27830): 230.81224400218002, (1, 27884): 202.5468309396555, (1, 27885): 207.78269729080802, (1, 27896): 204.6235322748685, (1, 27919): 204.41467585915538, (1, 27922): 205.05378341792348, (1, 27930): 203.35468177647323, (1, 27934): 203.54753795501506, (1, 27935): 203.6867210425933, (1, 27948): 228.45272918442424, (1, 27951): 229.75309694715068, (1, 28061): 206.2636412639015, (1, 28290): 250.49822458147278, (1, 28292): 251.2177214108507, (1, 28293): 250.62453842067254, (1, 28295): 250.13528406984744, (1, 28296): 250.39308975777735, (1, 28297): 250.10267785756452, (1, 28302): 249.685202118564, (1, 28310): 253.30858074111302, (1, 28313): 253.58628967412267, (1, 28372): 254.4598360825178, (1, 28398): 254.47353222412363, (1, 28399): 254.14093509894008, (1, 28400): 254.58252280190632, (1, 28401): 253.5177633853104, (1, 28445): 252.93407635485775, (1, 28475): 253.1520833444574, (1, 28885): 41.560736502413974, (1, 28886): 42.10930727324793, (1, 28915): 43.316393644351876, (1, 28916): 43.0425202737966, (1, 28917): 43.45206037826728, (1, 28921): 40.880544287886224, (1, 28931): 41.30290444068422, (1, 28945): 46.982953132593366, (1, 28982): 45.1841871279815, (1, 29219): 51.97187671562554, (1, 29228): 52.26670294860533, (1, 29246): 55.64007802932033, (1, 29248): 57.215127696846075, (1, 29282): 56.584648819836886, (1, 29290): 54.17009690951571, (1, 29291): 54.53935609416016, (1, 29292): 54.420889222847386, (1, 29293): 54.22811600770232, (1, 29294): 55.0521870188532, (1, 29298): 54.659675979876205, (1, 29299): 55.068064722175905, (1, 29304): 53.96844071519186, (1, 29317): 53.07481360528521, (1, 29323): 52.96321752977344, (1, 29330): 53.447332455534536, (1, 29331): 53.34655316734703, (1, 29344): 54.98550941749643, (1, 29445): 66.7465722430096, (1, 29724): 305.63382092302317, (1, 29738): 305.9933686482546, (1, 29745): 304.8056322701299, (1, 29748): 304.3063689829246, (1, 29750): 304.5952666248918, (1, 29759): 303.90048596856275, (1, 29772): 305.21747659010987, (1, 29781): 304.9095960732868, (1, 29784): 304.98735255258634, (1, 29790): 305.07169661647606, (1, 29811): 304.0074819677959, (1, 29817): 304.5805536242385, (1, 29818): 304.268292929936, (1, 29929): 305.11841937200444, (1, 30039): 311.7293686016728, (1, 30066): 309.79750620864337, (1, 30116): 296.11185543672224, (1, 30238): 275.9621645608572, (1, 30248): 287.8363611740607, (1, 30260): 288.2313052590619, (1, 30545): 40.36365278152315, (1, 30733): 52.08036600176535, (1, 30756): 60.797735253810416, (1, 30921): 51.771243041486095, (1, 31079): 91.74322413185551, (1, 31149): 93.11187217702461, (1, 31154): 93.21258136206228, (1, 31160): 93.23792970641257, (1, 31163): 93.5062835151694, (1, 31189): 101.04340166430099, (1, 31215): 100.69307838940462, (1, 31259): 102.28812596840748, (1, 31262): 103.04449242161857, (1, 31430): 91.75661006031739, (1, 31568): 114.3473949654305, (1, 31751): 96.29991568821009, (3, 109): 17.19733191869444, (3, 872): 205.4601388303383, (3, 873): 206.39813477701168, (3, 877): 206.16852835190954, (3, 879): 206.31956881790765, (3, 884): 205.65152045756932, (3, 889): 206.18090042663155, (3, 891): 205.3083647575202, (3, 892): 207.02132324161948, (3, 894): 206.85286527534424, (3, 896): 205.74618344022448, (3, 903): 206.3435289365608, (3, 909): 204.34524274524128, (3, 910): 204.60744131685706, (3, 912): 204.01381198040235, (3, 913): 203.40155049441464, (3, 916): 202.97656403810964, (3, 926): 204.76627931361483, (3, 927): 204.42607728047312, (3, 948): 204.9487406672221, (3, 961): 204.9976064182154, (3, 962): 205.0249841410808, (3, 963): 205.08129998469988, (3, 967): 206.69030325523, (3, 974): 206.47319427040813, (3, 998): 207.16203298072935, (3, 1014): 226.216032641746, (3, 1086): 199.8712737775993, (3, 1087): 199.35073869737764, (3, 1089): 198.6986365115877, (3, 1090): 199.12589198734204, (3, 1092): 200.47488670731906, (3, 1097): 199.52544554215743, (3, 1107): 200.8921756018, (3, 1387): 60.22906771429352, (3, 1554): 49.98539110249349, (3, 1827): 250.77871127616243, (3, 1828): 250.82603302912497, (3, 1829): 251.00558210000943, (3, 1830): 251.10273602628155, (3, 1831): 251.14310420059357, (3, 1832): 251.0183315906076, (3, 1833): 250.9874825878176, (3, 1836): 250.8318076854011, (3, 1841): 251.49522067191967, (3, 1843): 251.24323405594373, (3, 1844): 251.39724642511584, (3, 1845): 251.1340092301143, (3, 1847): 250.03909802420625, (3, 1848): 250.38874658763302, (3, 1849): 252.068962352799, (3, 1850): 252.20165920439948, (3, 1851): 250.7684823241212, (3, 1852): 250.89105306541447, (3, 1854): 250.98152658224245, (3, 1856): 250.11831271231384, (3, 1857): 250.41803400221812, (3, 1858): 251.84234777415944, (3, 1861): 251.06741808991038, (3, 1866): 250.1802876490183, (3, 1867): 251.43053211974112, (3, 1868): 251.14866107545208, (3, 1870): 251.49482700996, (3, 1871): 251.30293203470362, (3, 1875): 250.898193863909, (3, 1880): 250.24855365870795, (3, 1882): 250.4899510927679, (3, 1883): 252.10444628557715, (3, 1889): 250.2658488654386, (3, 1893): 250.8650793004607, (3, 1894): 250.59798273860295, (3, 1899): 249.98806465832752, (3, 1900): 250.13116033100073, (3, 1902): 251.28030450907957, (3, 1905): 251.65264066698475, (3, 1907): 250.5211752594911, (3, 1910): 250.51465141085458, (3, 1917): 251.98458359333168, (3, 1920): 250.4584661583457, (3, 1935): 251.50766394590306, (3, 1937): 251.80255650719192, (3, 1946): 249.23603208176382, (3, 1949): 249.47712954233333, (3, 1950): 248.70258910957494, (3, 1951): 249.1301687735146, (3, 1952): 249.7513497424143, (3, 1953): 249.677637297773, (3, 1954): 249.61700964776148, (3, 1958): 249.5001186072272, (3, 1960): 250.0560204391753, (3, 1968): 250.27479295319446, (3, 1969): 251.37843294969457, (3, 1974): 251.10684404403517, (3, 1975): 251.16673282511522, (3, 1979): 250.34964629622937, (3, 1980): 250.4863670885083, (3, 1981): 250.56813688982098, (3, 1985): 250.68135376049068, (3, 1994): 248.7495468259727, (3, 2011): 250.54284994134173, (3, 2019): 253.23592137644937, (3, 2020): 252.8813190956207, (3, 2029): 251.7210374152815, (3, 2030): 252.6325238043296, (3, 2032): 251.62771055522387, (3, 2033): 252.14980623378918, (3, 2034): 252.23306568372067, (3, 2036): 251.43203053508037, (3, 2037): 251.62186972384313, (3, 2038): 251.28266962680775, (3, 2042): 255.06969665070815, (3, 2050): 251.84226821299896, (3, 2051): 251.8892169311026, (3, 2053): 251.9451190284589, (3, 2054): 252.28364156954612, (3, 2066): 251.61262615489323, (3, 2067): 251.56277739861991, (3, 2071): 248.0683380486512, (3, 2072): 248.6145184735526, (3, 2073): 246.64751762958008, (3, 2074): 246.62829323003743, (3, 2080): 245.74410608666835, (3, 2082): 248.93194256825527, (3, 2083): 249.20825345187404, (3, 2089): 248.4588163161799, (3, 2090): 248.6992351962809, (3, 2092): 248.23699482314584, (3, 2098): 246.01261313397055, (3, 2099): 246.43208734069083, (3, 2101): 246.0375858789062, (3, 2102): 247.59894884193037, (3, 2103): 247.14458660901536, (3, 2104): 246.9387124891418, (3, 2106): 249.46283240594138, (3, 2112): 246.32920144181864, (3, 2113): 247.876723950717, (3, 2114): 248.40926474826932, (3, 2117): 249.77747443684035, (3, 2123): 243.87140895599242, (3, 2124): 244.19354204326137, (3, 2134): 243.5172219756284, (3, 2138): 244.36834797345676, (3, 2141): 243.55451161287203, (3, 2148): 244.9626693826513, (3, 2150): 242.81543668424214, (3, 2151): 243.2231962285226, (3, 2152): 242.70121967886817, (3, 2153): 244.9820539277712, (3, 2154): 243.58867037132705, (3, 2155): 243.5936671897522, (3, 2156): 243.23182591697432, (3, 2157): 244.149420051907, (3, 2160): 245.26981437713332, (3, 2161): 242.73873480393453, (3, 2162): 245.39371329471876, (3, 2163): 244.90961058111301, (3, 2164): 244.93633062508312, (3, 2168): 243.4268409852871, (3, 2172): 244.15805943352288, (3, 2174): 243.30221336452308, (3, 2178): 244.54871008300466, (3, 2179): 244.37588818402628, (3, 2183): 244.45470180252713, (3, 2185): 244.53291485817473, (3, 2186): 244.24501261783155, (3, 2190): 245.2305522390897, (3, 2192): 244.7321703936215, (3, 2193): 244.5126470621784, (3, 2194): 244.0039577361764, (3, 2195): 244.05466538592137, (3, 2197): 244.9020737597072, (3, 2205): 244.36605253590957, (3, 2207): 243.62970023057517, (3, 2208): 244.06630975313328, (3, 2212): 244.3889981705644, (3, 2214): 236.3714528765428, (3, 2225): 237.9094986669834, (3, 2231): 232.92006722934454, (3, 2278): 243.64143313499792, (3, 2284): 244.8649955815646, (3, 2285): 244.8040119660808, (3, 2291): 243.32055478411823, (3, 2292): 242.8843414612616, (3, 2307): 244.21668796671227, (3, 2313): 243.2858379582889, (3, 2317): 241.86313402122036, (3, 2319): 243.30105958212297, (3, 2321): 243.8794570730897, (3, 2323): 243.63278888277586, (3, 2326): 245.08115112425065, (3, 2327): 244.63667070837525, (3, 2329): 244.3523225525531, (3, 2330): 244.07191194658319, (3, 2332): 244.89057484129626, (3, 2344): 243.49202458373526, (3, 2346): 243.60003901460644, (3, 2361): 242.35240857362422, (3, 2368): 248.15777493413265, (3, 2374): 248.74674189999652, (3, 2375): 248.84679542506396, (3, 2377): 247.038221599369, (3, 2378): 249.210988601699, (3, 2379): 249.38301784726232, (3, 2380): 249.4613925756348, (3, 2383): 247.4179706390773, (3, 2385): 247.6383151549139, (3, 2395): 247.5536320759393, (3, 2397): 249.23671230044204, (3, 2398): 246.47628076572937, (3, 2399): 247.0370149923135, (3, 2400): 246.89521553998236, (3, 2402): 248.24000152813358, (3, 2403): 248.63480043925424, (3, 2404): 248.68387961004387, (3, 2405): 247.77977704095147, (3, 2407): 248.44000319866268, (3, 2408): 248.95782939041604, (3, 2409): 248.0339331073483, (3, 2411): 248.8454040324545, (3, 2412): 248.66178097612763, (3, 2413): 249.0148963641862, (3, 2414): 248.51750513641875, (3, 2422): 248.79971138934272, (3, 2424): 248.72636022458806, (3, 2426): 248.76842486710066, (3, 2433): 248.11808736413596, (3, 2436): 248.06282440826075, (3, 2437): 245.7276741715123, (3, 2440): 246.20414938187562, (3, 2445): 257.49117419369867, (3, 2447): 256.12585178202335, (3, 2454): 257.29445541894415, (3, 2455): 257.25859605991485, (3, 2460): 253.7644552259539, (3, 2461): 254.21777756645452, (3, 2471): 262.00314901324526, (3, 2492): 258.26351916452757, (3, 2511): 254.02495588726256, (3, 2523): 256.2072682953652, (3, 2525): 255.87776833906014, (3, 2535): 254.752114929231, (3, 2537): 254.02411220470123, (3, 2538): 254.42764303359442, (3, 2539): 254.68467711982487, (3, 2540): 255.0948419462226, (3, 2542): 255.79232009131286, (3, 2559): 265.8671588734979, (3, 2575): 265.44160334326665, (3, 2599): 247.30631697396086, (3, 2600): 251.38724631847936, (3, 2607): 248.65357878561915, (3, 2627): 257.9440492120136, (3, 2647): 260.3553102059252, (3, 2674): 258.7621918334507, (3, 2681): 258.7264477615119, (3, 2683): 259.6285068908203, (3, 2686): 258.33828515779976, (3, 2689): 272.13506575658874, (3, 2690): 272.2618647402677, (3, 2713): 276.70470035895477, (3, 2714): 277.1804416505808, (3, 2715): 277.5016073515764, (3, 2739): 277.14374159002364, (3, 2740): 274.42569916401453, (3, 2741): 274.5366804868102, (3, 2749): 276.96059160845687, (3, 2750): 276.97333739001095, (3, 2752): 277.16273061753327, (3, 2755): 277.4727132168094, (3, 2758): 277.4723308021911, (3, 2759): 277.4339353867383, (3, 2769): 276.95970350271256, (3, 2771): 275.12563477229537, (3, 2779): 275.86757488786884, (3, 2784): 272.5043823042515, (3, 2800): 273.788620683408, (3, 2802): 274.14276994449943, (3, 2803): 273.939208028678, (3, 2804): 273.6909455936553, (3, 2805): 274.658348163575, (3, 2807): 274.55669982258775, (3, 2809): 274.6178177252472, (3, 2812): 272.3314363838549, (3, 2814): 275.0466602512248, (3, 2817): 275.8443569927114, (3, 2819): 274.39964531870277, (3, 2823): 273.23714350755984, (3, 2832): 275.1763861999107, (3, 2836): 273.704126112941, (3, 2839): 274.4694360789887, (3, 2841): 275.5486980957791, (3, 2843): 275.30968307883313, (3, 2846): 274.32277989287695, (3, 2849): 275.54320051411094, (3, 2852): 275.1568987113987, (3, 2853): 275.72600878338517, (3, 2876): 276.25305061604143, (3, 2877): 277.48950709050746, (3, 2885): 278.6146167759453, (3, 2918): 274.0451253576753, (3, 2921): 274.65182783108554, (3, 2925): 271.5391625137719, (3, 2926): 270.34709040000024, (3, 2930): 273.45656552246805, (3, 2931): 271.98528900841046, (3, 2938): 274.19358937206346, (3, 2940): 275.00636227593424, (3, 2947): 273.083545062034, (3, 2949): 273.1199162056905, (3, 2950): 273.4892286582645, (3, 2952): 273.24117395679457, (3, 2958): 273.1344151426253, (3, 2959): 273.2155472046942, (3, 2960): 273.8315886078589, (3, 2961): 273.6259017994643, (3, 2963): 273.00184318064026, (3, 2968): 273.24549016257123, (3, 2976): 272.8498029377939, (3, 2981): 269.08223528692355, (3, 2982): 269.11272399396023, (3, 2984): 268.9044594301406, (3, 3003): 268.6563242087646, (3, 3046): 263.5081277516026, (3, 3050): 266.95809356102495, (3, 3051): 267.08945129028757, (3, 3053): 266.6152876465441, (3, 3069): 269.93689953520715, (3, 3071): 266.10014831727904, (3, 3080): 278.8987745697406, (3, 3199): 268.87568198711045, (3, 3200): 268.4198255247802, (3, 3205): 271.83166037162397, (3, 3209): 268.7360596159748, (3, 3215): 268.36219622031706, (3, 3217): 267.68751335405545, (3, 3249): 268.32594294052643, (3, 3263): 273.38210935818876, (3, 3289): 269.6730362042693, (3, 3301): 270.07661292052444, (3, 3302): 269.74445342386787, (3, 3307): 269.41576858443847, (3, 3310): 270.3674541101127, (3, 3391): 275.59380530497253, (3, 3509): 156.07877900471695, (3, 3510): 155.59721733536574, (3, 3511): 155.7726598384988, (3, 3512): 155.34744999357324, (3, 3514): 155.33354862055882, (3, 3519): 157.9175908901856, (3, 3536): 156.67353167327317, (3, 3545): 157.28398500624044, (3, 3548): 156.3550413749562, (3, 3572): 157.1231937995872, (3, 3581): 157.0228449154946, (3, 3583): 156.09794702928738, (3, 3601): 159.04620064037775, (3, 3656): 158.8197828374154, (3, 3669): 159.08253030591345, (3, 3670): 159.56407783107812, (3, 3695): 156.6011924223054, (3, 3696): 156.9198201354782, (3, 3782): 154.02380636308166, (3, 3792): 153.87378629010354, (3, 3989): 107.73402595236387, (3, 4008): 110.42950598396236, (3, 4031): 111.35082334233235, (3, 4045): 109.34861619283421, (3, 4144): 108.4652412381125, (3, 4145): 104.62888993788232, (3, 4164): 107.15705850103687, (3, 4168): 105.78908901524346, (3, 4173): 105.35470659062854, (3, 4181): 103.71296078080793, (3, 4228): 103.36549939730615, (3, 4248): 101.06939255520803, (3, 4254): 81.2241613982157, (3, 4260): 81.85226552114648, (3, 4262): 82.42486986313602, (3, 4273): 82.58581968816841, (3, 4319): 70.54942110976245, (3, 4326): 70.3883635577242, (3, 4328): 70.67519828367756, (3, 4334): 70.76695832474122, (3, 4335): 70.43543865957326, (3, 4372): 37.798845838342444, (3, 4413): 47.138965247948306, (3, 4434): 37.18959759562122, (3, 4447): 37.57886758647643, (3, 4452): 37.42971431785145, (3, 4463): 29.3157824516345, (3, 4465): 29.15719073025853, (3, 4619): 50.70915639521558, (3, 4645): 51.83483534528319, (3, 4657): 51.92353116542861, (3, 4666): 51.63215688410571, (3, 4676): 52.69844153988175, (3, 4678): 52.77868813977888, (3, 4689): 52.45516242409279, (3, 4704): 57.910770938027056, (3, 4726): 77.84326360909932, (3, 4727): 77.50486004854396, (3, 4730): 76.82722612027095, (3, 4731): 77.16231878628794, (3, 4734): 76.74011813367578, (3, 4735): 76.53720351466336, (3, 4736): 76.80118107178092, (3, 4737): 76.3727752421794, (3, 4738): 76.53232786527691, (3, 4756): 76.9343329747634, (3, 4760): 74.66137289366047, (3, 4761): 74.62637500929203, (3, 4762): 74.33786381835695, (3, 4765): 74.89589874117242, (3, 4773): 78.39252975201092, (3, 4774): 78.2787157489998, (3, 4790): 78.13983194778598, (3, 4795): 77.7977871433065, (3, 4799): 78.5251291525702, (3, 4801): 79.49460517186212, (3, 4804): 77.68103552538892, (3, 4805): 77.40336147806032, (3, 4806): 78.43036786643216, (3, 4815): 78.27500003092294, (3, 4816): 79.0350126242765, (3, 4817): 79.4246439846418, (3, 4826): 78.85144455672985, (3, 4830): 78.46592328494287, (3, 4839): 75.65543374844749, (3, 4840): 76.0468159079376, (3, 4841): 75.4088348628105, (3, 4846): 75.13911045202344, (3, 4848): 75.24534871577912, (3, 4850): 75.58361410975502, (3, 4871): 70.84789691857704, (3, 4883): 74.02043607256824, (3, 4900): 72.14263389018255, (3, 4901): 71.8623685393183, (3, 4917): 54.76907337963465, (3, 4931): 52.61156872539282, (3, 4944): 54.84135717431188, (3, 4956): 53.183238929616174, (3, 4958): 53.4744621339359, (3, 4959): 53.313547147996715, (3, 4961): 53.47653551057421, (3, 4966): 52.863172559696544, (3, 5207): 50.533491181381265, (3, 5272): 12.5, (3, 5283): 12.5, (3, 5287): 12.5, (3, 5289): 12.5, (3, 5293): 12.5, (3, 5295): 12.5, (3, 5296): 12.5, (3, 5298): 12.5, (3, 5303): 12.5, (3, 5305): 12.5, (3, 5306): 12.5, (3, 5307): 12.5, (3, 5308): 12.5, (3, 5313): 12.5, (3, 5314): 12.5, (3, 5317): 12.5, (3, 5319): 12.5, (3, 5324): 12.5, (3, 5326): 12.5, (3, 5348): 12.5, (3, 5351): 12.5, (3, 5399): 12.5, (3, 5413): 12.5, (3, 5422): 12.5, (3, 5445): 12.5, (3, 5448): 12.5, (3, 5456): 12.5, (3, 5467): 12.5, (3, 5624): 12.5, (3, 5671): 17.889591053883898, (3, 5672): 17.19457369494948, (3, 5797): 28.913632423906922, (3, 5871): 19.513708391047622, (3, 5976): 12.5, (3, 6118): 225.00974812810648, (3, 6248): 238.8902228325925, (3, 6345): 79.02848595625792, (3, 6352): 80.87741020393516, (3, 6354): 78.324416341554, (3, 6359): 78.4232256170653, (3, 6376): 81.6921666673342, (3, 6378): 78.59355053744602, (3, 6381): 78.89118765940826, (3, 6383): 79.23531391582199, (3, 6396): 80.91748400747267, (3, 6399): 79.55745599527482, (3, 6408): 80.35653392981133, (3, 6409): 78.28033304237523, (3, 6419): 79.47696132866375, (3, 6422): 79.16894420789723, (3, 6423): 79.25329985650052, (3, 6424): 77.1430033172307, (3, 6439): 77.10621250465414, (3, 6464): 77.24200893804294, (3, 6465): 77.84042367047476, (3, 6469): 78.48387868807161, (3, 6470): 78.79884079387956, (3, 6472): 77.99093355945647, (3, 6480): 76.34052627737212, (3, 6486): 73.108318210595, (3, 6497): 74.08955995891117, (3, 6503): 74.69212234913286, (3, 6508): 75.87457478183458, (3, 6509): 74.91666707944147, (3, 6521): 75.20350356533794, (3, 6544): 74.0550039032445, (3, 6552): 76.71141559313315, (3, 6553): 76.87103114323914, (3, 6554): 77.05151089782001, (3, 6578): 76.63095750139215, (3, 6582): 75.46406639126674, (3, 6601): 76.27800467887451, (3, 6609): 76.15718654620017, (3, 6610): 75.82132241737064, (3, 6611): 76.51503748430956, (3, 6614): 77.04966705479075, (3, 6615): 76.76015606597677, (3, 6616): 75.6115784146221, (3, 6617): 76.03367449302759, (3, 6618): 74.78752182622445, (3, 6619): 77.04153419235071, (3, 6620): 75.15208163848949, (3, 6621): 75.22379315886548, (3, 6622): 75.50020481521247, (3, 6623): 76.57226047099427, (3, 6624): 76.24420601414059, (3, 6625): 76.51960984122204, (3, 6626): 77.24854185119433, (3, 6627): 77.48606313320316, (3, 6628): 74.72219286092619, (3, 6629): 75.6412220261987, (3, 6630): 77.38725261326836, (3, 6632): 75.91016186944681, (3, 6634): 77.27736222837054, (3, 6635): 75.52893246865317, (3, 6636): 75.44464742061548, (3, 6637): 75.8202808769553, (3, 6638): 76.93661370359064, (3, 6639): 77.2046410636685, (3, 6640): 77.1374957327245, (3, 6641): 74.87186136904879, (3, 6642): 76.6314953586945, (3, 6643): 77.58962653859417, (3, 6645): 76.81252686907871, (3, 6646): 75.20566600296384, (3, 6647): 76.74878842738872, (3, 6653): 76.9073438892332, (3, 6655): 77.35005452686498, (3, 6658): 77.1133629151036, (3, 6662): 76.31749313512917, (3, 6819): 81.72642816017853, (3, 6996): 71.4589163812845, (3, 7059): 68.8707865542862, (3, 7187): 60.92334320513315, (3, 7304): 74.63927104571594, (3, 7528): 65.9581267819418, (3, 7720): 57.51503651565208, (3, 7793): 55.071052873088824, (3, 7807): 55.79784263435577, (3, 7808): 54.51172986715421, (3, 7831): 71.8442119173559, (3, 7850): 72.37988426307693, (3, 7852): 73.41724572730612, (3, 8012): 61.664281793732044, (3, 8125): 42.121322828761286, (3, 8208): 54.610022641575625, (3, 8392): 63.16010399588404, (3, 8651): 95.61587494958233, (3, 9088): 90.47291834685616, (3, 9443): 88.46696237844789, (3, 9444): 87.7371853499202, (3, 9828): 101.17900513463265, (3, 9868): 105.67993243967983, (3, 10180): 40.75497641051824, (3, 10256): 35.941251750966074, (3, 10276): 40.051023303396335, (3, 10378): 46.930511554966294, (3, 10676): 32.92945183106688, (3, 10714): 35.908024745349564, (3, 10730): 41.13929012942801, (3, 10862): 55.655372127270844, (3, 10881): 55.15091583007507, (3, 10883): 55.457941456494694, (3, 10885): 55.706666497260734, (3, 10891): 55.9413508210865, (3, 10909): 55.382529522069994, (3, 10911): 54.694674810852675, (3, 10913): 55.01008749133651, (3, 10915): 54.69756114618325, (3, 10919): 54.359751205157536, (3, 11037): 65.74969670474077, (3, 11039): 65.11305653617168, (3, 11516): 146.33336519395206, (3, 11856): 70.94222605535374, (3, 11857): 69.76828823113925, (3, 11861): 70.34603586943894, (3, 11881): 71.17444113830597, (3, 11902): 69.91788231107255, (3, 11911): 70.58957055956033, (3, 11914): 70.3692586983999, (3, 11922): 70.9873110697644, (3, 11924): 71.51204111445476, (3, 11926): 71.20170274548744, (3, 11950): 72.88917069829738, (3, 11963): 73.94727164224143, (3, 11983): 74.73071934875365, (3, 11985): 74.40910622772155, (3, 12009): 75.50411941690648, (3, 12010): 74.42052457935846, (3, 12018): 74.72498687638604, (3, 12020): 74.73972947608392, (3, 12021): 75.01223366284128, (3, 12024): 75.75085545662819, (3, 12025): 75.23086716647252, (3, 12027): 75.12201380103164, (3, 12031): 74.2857884970768, (3, 12032): 74.32849459097393, (3, 12035): 75.76021794908989, (3, 12041): 73.73773776379188, (3, 12045): 65.82225342956765, (3, 12145): 71.25946000129363, (3, 12275): 111.17516211158524, (3, 12294): 110.50721454679416, (3, 12358): 118.55996919640778, (3, 12463): 122.67249835833344, (3, 12465): 122.67631812558766, (3, 12482): 122.6069153249414, (3, 12503): 122.75336493189926, (3, 12506): 123.04230961719674, (3, 12549): 120.94888883605977, (3, 12559): 121.02165604834173, (3, 12569): 121.77910682856675, (3, 12572): 121.96610364498608, (3, 12574): 121.41357392263293, (3, 12576): 121.02352224451316, (3, 12591): 120.1302841541971, (3, 12608): 121.27607144339366, (3, 12696): 117.91439803636433, (3, 12710): 118.44366083205837, (3, 12728): 118.82902399085974, (3, 12766): 83.82958641029155, (3, 12771): 79.0790078410443, (3, 12790): 79.13264548770513, (3, 12795): 79.76975764242047, (3, 12797): 76.44027824968616, (3, 12798): 76.3924727082276, (3, 12811): 77.36750416804833, (3, 12830): 77.78979009775207, (3, 12848): 76.41259084154275, (3, 12850): 75.56275174655102, (3, 12852): 77.28079358125794, (3, 12854): 77.14550951737414, (3, 12859): 76.14800847852112, (3, 12861): 76.18455841001064, (3, 12865): 78.23002610331781, (3, 12866): 77.69809250972477, (3, 12867): 78.41078966536958, (3, 12874): 78.1270356807846, (3, 12875): 78.04751198016679, (3, 12881): 78.10962590409657, (3, 12883): 78.23579913976172, (3, 12885): 78.25278478627095, (3, 12888): 77.8522211531425, (3, 12889): 77.5146009647672, (3, 12892): 78.3343962377408, (3, 12893): 78.17146675493808, (3, 12896): 77.94029712119955, (3, 12906): 79.52420736797086, (3, 13018): 86.5667225377918, (3, 13071): 88.37615838601992, (3, 13131): 80.58593192121232, (3, 13146): 79.5369237885857, (3, 13159): 88.29936545780775, (3, 13193): 79.98362760076232, (3, 13198): 76.64338044940975, (3, 13292): 76.13177172128528, (3, 13296): 73.08496368667555, (3, 13406): 81.78574683972411, (3, 13407): 82.19743335177756, (3, 13417): 85.3920417360013, (3, 13418): 85.86938709379066, (3, 13438): 83.26868783723248, (3, 13442): 82.19119418815806, (3, 13443): 82.34405725587136, (3, 13764): 117.19321857550469, (3, 13766): 116.82535499565685, (3, 13771): 118.20845178307766, (3, 13783): 115.79705472859675, (3, 13784): 115.98295083669474, (3, 13792): 120.45501704132336, (3, 13824): 116.2586713292058, (3, 14017): 108.1033141233467, (3, 14870): 43.20697263584841, (3, 14997): 62.467778564727766, (3, 15000): 61.94852966007457, (3, 15003): 61.12363369744351, (3, 15006): 62.424522745986344, (3, 15007): 62.02328349605653, (3, 15056): 60.62679800462164, (3, 15063): 60.6674196350437, (3, 15069): 60.25194826334911, (3, 15076): 61.62418779505789, (3, 15086): 63.34959503788605, (3, 15087): 63.064952245596146, (3, 15111): 64.61573652201166, (3, 15116): 63.67673397159593, (3, 15722): 73.92958299699794, (3, 15998): 71.91895311293827, (3, 16073): 197.23385929115955, (3, 16939): 225.3907213532962, (3, 16940): 224.68524260066954, (3, 16951): 225.84259293998687, (3, 16963): 225.8228533053773, (3, 16965): 226.5254780089556, (3, 16969): 226.539688335236, (3, 16970): 226.00834652275725, (3, 16971): 225.3623850334243, (3, 16973): 225.44681067913342, (3, 16974): 226.93022882411074, (3, 16976): 225.97764112247737, (3, 16978): 225.46089584113778, (3, 16980): 226.1078751587854, (3, 16982): 227.05830194113398, (3, 17045): 257.8719967299329, (3, 17048): 258.7872853644682, (3, 17304): 95.82923160817751, (3, 17305): 96.24568755818083, (3, 17330): 96.35575554652306, (3, 17334): 94.94886307804857, (3, 17343): 97.0682967181092, (3, 17345): 95.75723247080239, (3, 17347): 96.84742473720179, (3, 17351): 93.95035125047077, (3, 17372): 95.18264170846602, (3, 17373): 96.89830033634763, (3, 17377): 97.08677031320674, (3, 17382): 96.14538580715461, (3, 17383): 96.04132409866786, (3, 17389): 95.55366295931401, (3, 17400): 96.37544340899807, (3, 17401): 96.22503768555865, (3, 17402): 96.51123047093965, (3, 17403): 96.67247293513682, (3, 17440): 96.7205976342347, (3, 17455): 97.45133720691732, (3, 17491): 98.15509571664909, (3, 17507): 92.45922855560829, (3, 17509): 92.74364308514524, (3, 17590): 94.56162143565184, (3, 17615): 86.44170979755195, (3, 17642): 87.35665829462326, (3, 17643): 87.63680661892535, (3, 17668): 86.21914845323171, (3, 17721): 83.23746855590493, (3, 17754): 87.42589929888858, (3, 17769): 91.67832972098732, (3, 17776): 91.2515140517036, (3, 17804): 92.33353402781471, (3, 17809): 92.82717917062615, (3, 17824): 91.98597315300324, (3, 17837): 93.0150940276849, (3, 17838): 93.5388466674182, (3, 17862): 93.40531972961858, (3, 17866): 94.21052995672862, (3, 17872): 92.77264553226445, (3, 17873): 92.27093894063698, (3, 17881): 93.11345888969385, (3, 17947): 165.00061476608383, (3, 17951): 164.0168287902027, (3, 17953): 163.6851069129806, (3, 17954): 163.6597256491085, (3, 17959): 165.04506572928958, (3, 17963): 164.94892401078454, (3, 18000): 159.56497536326188, (3, 18001): 159.56587108069232, (3, 18111): 168.56274443346703, (3, 18148): 139.90844544813885, (3, 18166): 150.13165387814166, (3, 18189): 161.34678268067938, (3, 18239): 96.83300340460916, (3, 18240): 96.91757305557174, (3, 18245): 96.92554711221544, (3, 18247): 96.91474670973506, (3, 18251): 97.03372043119307, (3, 18256): 97.2680169371679, (3, 18258): 97.19743486484863, (3, 18259): 97.26827049403322, (3, 18260): 97.38406796032626, (3, 18262): 97.53758332405394, (3, 18263): 97.35172052499934, (3, 18264): 97.46109358223477, (3, 18266): 97.65448813427831, (3, 18267): 97.74875317387814, (3, 18268): 97.82887580139304, (3, 18269): 98.02635002113135, (3, 18275): 97.93359469545109, (3, 18285): 97.38825044912137, (3, 18308): 95.31493632640293, (3, 18313): 94.86702821098832, (3, 18314): 95.35420445070763, (3, 18315): 97.76634566927153, (3, 18316): 97.87399884884556, (3, 18317): 97.97398830613423, (3, 18320): 97.89290361928184, (3, 18321): 98.00246276620624, (3, 18322): 98.13539514701966, (3, 18324): 98.071258918376, (3, 18325): 98.31691723813248, (3, 18326): 98.21982064867258, (3, 18327): 98.16673338406784, (3, 18329): 98.29257053996153, (3, 18330): 98.54520673352734, (3, 18331): 98.3215107208928, (3, 18332): 98.15352396741783, (3, 18333): 98.41220549379507, (3, 18336): 98.09374216077883, (3, 18337): 98.10014737082663, (3, 18403): 98.65488172766536, (3, 18432): 98.89472948356746, (3, 18451): 98.73954514775498, (3, 18466): 98.3039563145772, (3, 18481): 97.5096097903095, (3, 18483): 97.59514356547761, (3, 18484): 97.39422360760321, (3, 18485): 96.70180511467461, (3, 18486): 96.75800982934054, (3, 18487): 96.3382344612313, (3, 18489): 97.01198574035205, (3, 18490): 97.09306024246513, (3, 18491): 97.24135467723005, (3, 18492): 96.09402256670512, (3, 18493): 96.60240595587769, (3, 18494): 97.02153566054383, (3, 18495): 96.96967066594317, (3, 18496): 96.88502673719424, (3, 18497): 96.16159851499334, (3, 18498): 96.58567595981822, (3, 18499): 96.8488339193476, (3, 18501): 96.50572174275541, (3, 18502): 96.32733077456307, (3, 18503): 96.29584364941634, (3, 18504): 97.05267650897335, (3, 18506): 96.28238826317387, (3, 18507): 96.06289144509861, (3, 18508): 96.72840281929727, (3, 18509): 96.64982262879975, (3, 18510): 96.17915373613728, (3, 18511): 96.47687247446702, (3, 18512): 96.44277434017648, (3, 18515): 96.94604111134143, (3, 18516): 96.67542496821758, (3, 18517): 96.32617193983346, (3, 18518): 96.88951092502813, (3, 18519): 97.13855502016952, (3, 18520): 96.78212979040775, (3, 18522): 98.01000367065886, (3, 18523): 97.95023134248484, (3, 18532): 98.03824700635829, (3, 18535): 97.7590887836735, (3, 18537): 97.60403453265951, (3, 18539): 97.58721402423883, (3, 18540): 97.55322217820984, (3, 18541): 97.58661819130388, (3, 18542): 97.61684892630863, (3, 18543): 97.42850432443393, (3, 18546): 97.35775874867346, (3, 18555): 97.5928205570594, (3, 18556): 97.5715437540747, (3, 18565): 97.89348330327256, (3, 18567): 97.7777502960405, (3, 18568): 97.72811794365711, (3, 18577): 98.69598290840865, (3, 18583): 98.79054116227205, (3, 18605): 99.30399767493118, (3, 18608): 97.48406233811293, (3, 18616): 100.19558941473905, (3, 18618): 100.79935669714314, (3, 18625): 101.21454797031421, (3, 18645): 100.8151205016656, (3, 18646): 100.76716361060582, (3, 18653): 99.47456654473675, (3, 18654): 100.06469452036717, (3, 18655): 99.53603816587247, (3, 18666): 103.1935935678172, (3, 18837): 110.51055808065479, (3, 18974): 100.93141667433906, (3, 18999): 102.7327383149028, (3, 19000): 102.9832112073464, (3, 19174): 98.78398087222061, (3, 19342): 105.27980492039772, (3, 19455): 95.30530631646391, (3, 19555): 89.41874073612817, (3, 19564): 93.25154325053091, (3, 19573): 92.17192162598062, (3, 19586): 91.474058284173, (3, 19605): 91.07929795132614, (3, 19611): 91.68320268490156, (3, 19614): 90.50163426113502, (3, 19641): 96.7857344260035, (3, 19702): 97.6832573689974, (3, 19713): 97.00183215242853, (3, 19731): 83.06598380592033, (3, 19819): 95.64517338469986, (3, 19893): 37.31886250818091, (3, 19899): 37.63602683555489, (3, 19929): 38.0094017522348, (3, 19951): 41.42720813157188, (3, 19962): 36.97259381987248, (3, 19970): 40.15330154750822, (3, 19971): 39.58251959222415, (3, 19972): 38.90179740088604, (3, 19975): 39.198616363256285, (3, 19978): 44.60940311142801, (3, 19987): 45.02876190020606, (3, 19989): 43.94293358585143, (3, 20039): 45.40815258020434, (3, 20043): 46.37055866020489, (3, 20047): 46.43321615438723, (3, 20052): 44.84279256750963, (3, 20054): 44.692730670952876, (3, 20085): 53.886169105680466, (3, 20104): 54.407578706327286, (3, 20132): 50.82270963208817, (3, 20203): 31.72301561998202, (3, 20280): 29.656695525846047, (3, 20285): 28.866931582458708, (3, 20290): 30.1621979757579, (3, 20297): 29.929977517501715, (3, 20309): 41.49851240536683, (3, 20453): 52.29665322479628, (3, 20485): 28.81487147433459, (3, 20520): 28.797233779276635, (3, 20526): 26.57964591014903, (3, 20698): 144.50144050294233, (3, 20868): 161.43038896038132, (3, 21042): 56.982035275000605, (3, 21057): 58.71730255417316, (3, 21066): 56.82007213792715, (3, 21075): 57.94486941522399, (3, 21093): 55.70320256009302, (3, 21098): 54.86603661831431, (3, 21127): 56.36716715942192, (3, 21130): 55.982146945477794, (3, 21144): 57.252787227557626, (3, 21146): 56.274303484162836, (3, 21147): 57.62021080623574, (3, 21148): 57.43752408408762, (3, 21153): 61.91675069653691, (3, 21293): 58.17682629807039, (3, 21426): 70.14529717684906, (3, 21442): 74.56875134878162, (3, 21451): 74.95249541016669, (3, 21466): 71.66295530063023, (3, 21469): 71.72229860362096, (3, 21471): 71.66233832250116, (3, 21473): 71.55884605375275, (3, 21475): 71.48644011176616, (3, 21482): 72.25774507565706, (3, 21484): 71.98344130620366, (3, 21488): 72.08068042512507, (3, 21494): 70.79697626202363, (3, 21498): 71.01452758612352, (3, 21500): 70.12733454032585, (3, 21514): 67.9973331667561, (3, 21537): 68.54524303797206, (3, 21662): 66.393253880971, (3, 21691): 65.54116633811255, (3, 21757): 69.57119504479485, (3, 21777): 50.672576434698165, (3, 21778): 50.70274504769548, (3, 21779): 50.03047195221753, (3, 21790): 51.36204644508045, (3, 21802): 50.07800334652515, (3, 21824): 49.415993841612384, (3, 21874): 49.21890439275581, (3, 21879): 48.038954041524235, (3, 21983): 54.63275601068226, (3, 22002): 50.97286190824852, (3, 22132): 65.5429042380881, (3, 22261): 99.5518984514822, (3, 22298): 97.5961753463875, (3, 22339): 104.49523155714091, (3, 22508): 86.34900256963982, (3, 22841): 282.3998437790951, (3, 22842): 282.33179588680906, (3, 22874): 280.3186695373527, (3, 22941): 280.74418803060775, (3, 22956): 281.7615431280471, (3, 22960): 282.2517829464335, (3, 22968): 282.3269625371826, (3, 22970): 282.76687133165177, (3, 22974): 282.66669505724633, (3, 22980): 283.9554850061676, (3, 23025): 282.9001351095544, (3, 23028): 282.4189840969781, (3, 23081): 283.4138967294858, (3, 23104): 279.4392300221234, (3, 23147): 270.7881574475541, (3, 23298): 69.60827855916314, (3, 23376): 68.34969779927795, (3, 23381): 64.71070327852068, (3, 23529): 68.09966279906935, (3, 23556): 67.7062044492532, (3, 23718): 71.22987606012256, (3, 24001): 78.44711208630933, (3, 24094): 76.80309900612316, (3, 24129): 78.39463983383966, (3, 24174): 73.34718878466973, (3, 24235): 75.74578774611106, (3, 24259): 78.43644439762323, (3, 24260): 78.14779092824274, (3, 24261): 77.95800892120923, (3, 24305): 80.78907307677268, (3, 24306): 80.88648948903082, (3, 24307): 80.532006116598, (3, 24308): 85.18082613189439, (3, 24498): 88.31489150805169, (3, 24499): 88.27317764320904, (3, 24500): 88.04809229583866, (3, 24668): 90.23245509662968, (3, 24711): 88.65306090518507, (3, 24756): 88.40065506949324, (3, 24788): 89.4767914351202, (3, 24809): 86.17782522339219, (3, 24813): 87.3241598561055, (3, 24821): 87.00077612019487, (3, 24825): 87.0110219447951, (3, 24832): 86.13790662601821, (3, 24833): 86.50896673454949, (3, 24835): 86.80942489631573, (3, 24837): 87.56328528697408, (3, 24840): 85.99656215898676, (3, 24841): 86.74353495794998, (3, 24844): 85.89987886005056, (3, 24845): 86.6814625506194, (3, 24846): 86.02559820741004, (3, 24849): 86.17394029074421, (3, 24850): 87.29937206437855, (3, 24863): 82.99759487312987, (3, 24866): 83.69542786383087, (3, 24885): 84.08866183652859, (3, 24886): 83.89597701487877, (3, 24889): 86.23766570426336, (3, 24903): 87.1894823053801, (3, 24909): 85.3962311668544, (3, 24999): 117.0848343733851, (3, 25019): 117.14736362693246, (3, 25028): 116.49212101430125, (3, 25137): 25.126036504219492, (3, 25145): 25.953605488190338, (3, 25208): 33.13334924067579, (3, 25233): 31.95164266836989, (3, 25371): 28.11549462585761, (3, 25377): 27.046030982142035, (3, 25828): 26.308316238421515, (3, 25851): 33.4906768892102, (3, 25874): 28.147262911849992, (3, 25898): 23.793785375506566, (3, 25946): 26.949323232644574, (3, 26047): 12.691037243604764, (3, 26066): 28.458415177793405, (3, 26197): 18.94253360132512, (3, 26212): 41.5669468374305, (3, 26253): 43.554597325382886, (3, 26254): 42.83852285073804, (3, 26257): 41.99216973097716, (3, 26258): 43.11076617830067, (3, 26260): 42.54581602872447, (3, 26266): 43.66680811937216, (3, 26267): 42.94766931060294, (3, 26271): 42.875662701990834, (3, 26304): 36.64042489018692, (3, 26305): 36.93434877195197, (3, 26363): 25.705368455236794, (3, 26441): 93.79462135133119, (3, 26442): 93.70599289385908, (3, 26450): 92.5354348590896, (3, 26459): 91.83608624898254, (3, 26462): 91.73352750353945, (3, 26467): 95.08010671398321, (3, 26471): 94.4405938879783, (3, 26472): 94.42952357977613, (3, 26473): 94.47656561383225, (3, 26476): 94.83643225636392, (3, 26485): 92.70344240396958, (3, 26493): 93.05163733405976, (3, 26524): 91.96889300886251, (3, 26525): 92.00046094171506, (3, 26556): 93.95946353139932, (3, 26560): 93.35356603082508, (3, 26561): 92.51475325983851, (3, 26564): 93.78743472785615, (3, 26569): 92.50160349809418, (3, 26570): 92.40350365870299, (3, 26573): 92.85542238389158, (3, 26581): 93.06981199172162, (3, 26583): 92.67110170574486, (3, 26593): 93.38463092171291, (3, 26837): 95.5472133640321, (3, 26844): 96.20295877925192, (3, 26863): 95.36484584078708, (3, 26893): 97.4788025875275, (3, 26902): 98.38806735900539, (3, 26905): 96.94971944794221, (3, 26912): 97.82518327072238, (3, 26921): 96.34009524319846, (3, 26922): 95.39330967193425, (3, 27212): 90.78728739039117, (3, 27218): 89.52761407516176, (3, 27239): 92.33978315498112, (3, 27257): 91.68506096752016, (3, 27274): 92.70618627764206, (3, 27279): 92.66895903461125, (3, 27282): 91.78963585252654, (3, 27283): 91.88910953542792, (3, 27285): 93.18084940781017, (3, 27286): 92.5989682872536, (3, 27290): 91.0598652939231, (3, 27295): 90.32566011889466, (3, 27300): 92.8081754849453, (3, 27344): 91.0429754849016, (3, 27366): 92.16440815188159, (3, 27383): 93.52602238566699, (3, 27398): 94.28915821431808, (3, 27406): 93.32101413227068, (3, 27407): 93.48131668874575, (3, 27426): 91.50004937313226, (3, 27432): 87.92759763069411, (3, 27460): 90.05131371906786, (3, 27523): 94.66617109087294, (3, 27545): 107.8504276911946, (3, 27602): 128.98335179290927, (3, 27606): 129.22347213364876, (3, 27646): 110.3312292033003, (3, 27667): 114.43673940847694, (3, 27672): 114.54948700434694, (3, 27674): 113.91259660666331, (3, 27688): 114.09748799347436, (3, 27692): 115.37823081305578, (3, 27693): 114.78429904915262, (3, 27705): 114.86960741789453, (3, 27712): 115.261011635985, (3, 27786): 126.7723501194334, (3, 27790): 123.47452567140193, (3, 27791): 123.14520891425963, (3, 27795): 125.68817378979347, (3, 27801): 123.3046774671819, (3, 27813): 127.52768236963128, (3, 27816): 126.57122856245653, (3, 27823): 123.20637281570146, (3, 27830): 125.42662882118283, (3, 27884): 104.80331359297358, (3, 27885): 108.79937305999748, (3, 27896): 106.3020872077245, (3, 27919): 106.0111319719075, (3, 27922): 106.6887534072135, (3, 27930): 105.24339798518838, (3, 27934): 105.50592983288587, (3, 27935): 105.74482410579189, (3, 27948): 131.82421205615208, (3, 27951): 131.21857839497278, (3, 28061): 129.75806856789714, (3, 28290): 166.11171137555166, (3, 28292): 167.42302229555312, (3, 28293): 166.40659604609218, (3, 28295): 166.38061456991633, (3, 28296): 166.23877585931294, (3, 28297): 165.4501326816488, (3, 28302): 165.44543358262285, (3, 28310): 205.1451127192236, (3, 28313): 206.4316848380616, (3, 28372): 205.31078382150298, (3, 28398): 205.4701250546325, (3, 28399): 205.2777058180496, (3, 28400): 205.75157500725072, (3, 28401): 204.35189978408118, (3, 28445): 206.39962666015433, (3, 28475): 202.52646075266713, (3, 28885): 68.92330030895609, (3, 28886): 68.33718697198819, (3, 28915): 67.4544648913183, (3, 28916): 67.56350510044985, (3, 28917): 67.15180118990641, (3, 28921): 69.73424016846674, (3, 28931): 69.3490338724712, (3, 28945): 63.9977650758891, (3, 28982): 65.63941852008963, (3, 29219): 61.38919034942667, (3, 29228): 60.26468836148326, (3, 29246): 65.45210294310311, (3, 29248): 64.37192169687451, (3, 29282): 62.91340564742377, (3, 29290): 67.27462301266375, (3, 29291): 66.66968650233142, (3, 29292): 67.09742359017962, (3, 29293): 66.48051513796372, (3, 29294): 66.5614093577464, (3, 29298): 66.2698420782826, (3, 29299): 65.95670786698584, (3, 29304): 65.96360019631281, (3, 29317): 64.88682543165042, (3, 29323): 64.83668944369654, (3, 29330): 65.2980511909257, (3, 29331): 65.75677185719408, (3, 29344): 59.3216499681942, (3, 29445): 42.54984196591443, (3, 29724): 281.8613124653329, (3, 29738): 282.20074902965763, (3, 29745): 281.2992139016369, (3, 29748): 281.943079702575, (3, 29750): 282.6861515213805, (3, 29759): 281.42255860801, (3, 29772): 282.6851450892371, (3, 29781): 282.4223308913677, (3, 29784): 282.01408088221774, (3, 29790): 282.77591276955957, (3, 29811): 282.2549247812209, (3, 29817): 285.7406953293042, (3, 29818): 285.4918187493197, (3, 29929): 280.8995264326521, (3, 30039): 284.0545352856349, (3, 30066): 280.4506415772357, (3, 30116): 269.9031303215687, (3, 30238): 254.1670331550054, (3, 30248): 260.5948099039371, (3, 30260): 260.6534441561119, (3, 30545): 68.89976920938096, (3, 30733): 62.493101171611094, (3, 30756): 53.47444544093823, (3, 30921): 59.642092034385385, (3, 31079): 92.48412660494796, (3, 31149): 86.63330698367412, (3, 31154): 87.60425682367806, (3, 31160): 86.50178787345857, (3, 31163): 87.58801438807434, (3, 31189): 85.5386104583953, (3, 31215): 86.51206919517779, (3, 31259): 90.77046186564297, (3, 31262): 90.35797772366139, (3, 31430): 95.51239069953657, (3, 31568): 101.78315079794142, (3, 31751): 94.11811813140535, (5, 109): 88.42706701633514, (5, 872): 258.8106367315767, (5, 873): 259.7178201722269, (5, 877): 259.3941279548886, (5, 879): 259.5303148913509, (5, 884): 258.65594052635225, (5, 889): 259.21661677984315, (5, 891): 258.3513508520324, (5, 892): 260.230090962231, (5, 894): 260.1087722473353, (5, 896): 259.20701580990703, (5, 903): 259.4471124095219, (5, 909): 257.8478487834356, (5, 910): 258.1956274252254, (5, 912): 257.59917847870224, (5, 913): 256.94769573259913, (5, 916): 256.6491872560166, (5, 926): 258.4727839716239, (5, 927): 258.1646269017994, (5, 948): 258.0198687392272, (5, 961): 258.4766196322169, (5, 962): 258.56878954693013, (5, 963): 258.6758599326288, (5, 967): 259.8239242360433, (5, 974): 259.375692222507, (5, 998): 260.1964433894658, (5, 1014): 279.8173266321999, (5, 1086): 256.088406833911, (5, 1087): 255.90599816748278, (5, 1089): 255.10296117483009, (5, 1090): 255.49175419849257, (5, 1092): 256.80220146686077, (5, 1097): 255.81604946730067, (5, 1107): 257.411527225207, (5, 1387): 118.53523973665791, (5, 1554): 104.5837489178984, (5, 1827): 300.4269320043442, (5, 1828): 300.51946861777344, (5, 1829): 300.660718811776, (5, 1830): 300.5337753334715, (5, 1831): 300.6120551564946, (5, 1832): 300.51307395921054, (5, 1833): 300.52120203133734, (5, 1836): 300.4136984658875, (5, 1841): 300.9977323804604, (5, 1843): 300.7547745426009, (5, 1844): 300.86570921340746, (5, 1845): 300.57886537708094, (5, 1847): 299.6342109518911, (5, 1848): 299.9576970858939, (5, 1849): 301.4763412680596, (5, 1850): 301.6325375990617, (5, 1851): 300.2127118573149, (5, 1852): 300.24278602121666, (5, 1854): 300.39261998313225, (5, 1856): 299.5968781240296, (5, 1857): 299.9391775481202, (5, 1858): 301.3245426850128, (5, 1861): 300.64596463526067, (5, 1866): 299.5818338511665, (5, 1867): 301.00900055959636, (5, 1868): 300.80855495611667, (5, 1870): 300.8471917269009, (5, 1871): 300.9593921334356, (5, 1875): 300.3718585163426, (5, 1880): 299.79354103013316, (5, 1882): 299.8983777639087, (5, 1883): 301.6377359815327, (5, 1889): 299.95138236734925, (5, 1893): 300.66735278447453, (5, 1894): 300.4370555005066, (5, 1899): 299.74540251957234, (5, 1900): 299.9113430623778, (5, 1902): 301.0635209401127, (5, 1905): 301.3624290387969, (5, 1907): 300.170609345381, (5, 1910): 300.27087947005907, (5, 1917): 301.95995523019866, (5, 1920): 300.18675422411405, (5, 1935): 301.38958399605576, (5, 1937): 301.64279765354655, (5, 1946): 299.2221554595941, (5, 1949): 299.4990551036117, (5, 1950): 298.5319015481916, (5, 1951): 299.0026209011493, (5, 1952): 299.3769967110305, (5, 1953): 299.5145194024785, (5, 1954): 299.3031045019196, (5, 1958): 299.4272239940565, (5, 1960): 299.908528967375, (5, 1968): 300.09840152235967, (5, 1969): 301.4332072928078, (5, 1974): 301.0854858220239, (5, 1975): 301.0866585743097, (5, 1979): 300.40050244286004, (5, 1980): 300.36259461854115, (5, 1981): 300.5506868215158, (5, 1985): 300.70923182687307, (5, 1994): 298.1830125759226, (5, 2011): 299.89124474419447, (5, 2019): 302.27254718160884, (5, 2020): 301.95782327685725, (5, 2029): 300.77641905815153, (5, 2030): 301.7394480146778, (5, 2032): 300.59028730688436, (5, 2033): 301.2109813610574, (5, 2034): 301.20694117961864, (5, 2036): 300.051231500936, (5, 2037): 300.3460470786055, (5, 2038): 300.41609271230357, (5, 2042): 304.02256981943196, (5, 2050): 301.0384437196451, (5, 2051): 300.9939165852732, (5, 2053): 301.0863621907356, (5, 2054): 301.40574374039727, (5, 2066): 300.7571160817996, (5, 2067): 300.7553272659808, (5, 2071): 297.57704210995246, (5, 2072): 298.1687160583469, (5, 2073): 296.5060261792242, (5, 2074): 296.43055794812375, (5, 2080): 295.43464292776935, (5, 2082): 298.4896525411222, (5, 2083): 298.7950920688642, (5, 2089): 298.1331948931786, (5, 2090): 298.4166056229817, (5, 2092): 298.0183673172234, (5, 2098): 295.8094488702507, (5, 2099): 296.16291584655295, (5, 2101): 295.75471747423524, (5, 2102): 297.3743645994109, (5, 2103): 296.86844868535997, (5, 2104): 296.5956282422836, (5, 2106): 299.007185676975, (5, 2112): 295.9777353732753, (5, 2113): 297.61000241607326, (5, 2114): 298.0146441949775, (5, 2117): 299.25741449532245, (5, 2123): 296.5004604394995, (5, 2124): 296.83423003701876, (5, 2134): 295.9148241830742, (5, 2138): 296.88432327754606, (5, 2141): 296.02080742283437, (5, 2148): 296.62775832407965, (5, 2150): 295.2142700498345, (5, 2151): 295.5745288886428, (5, 2152): 295.0380149282706, (5, 2153): 296.729486726152, (5, 2154): 295.3390637642996, (5, 2155): 295.1992969693067, (5, 2156): 294.9280189069974, (5, 2157): 295.34873606134374, (5, 2160): 297.40939471336804, (5, 2161): 294.9924796988706, (5, 2162): 296.830912635429, (5, 2163): 296.3581202297402, (5, 2164): 296.33356522915136, (5, 2168): 295.4110249146599, (5, 2172): 295.7763692861164, (5, 2174): 295.5494364546859, (5, 2178): 296.06573204518446, (5, 2179): 295.8541011165932, (5, 2183): 296.87573712020975, (5, 2185): 296.9043356619755, (5, 2186): 296.6338779713547, (5, 2190): 297.4616670708766, (5, 2192): 296.9773323002598, (5, 2193): 296.9650674797867, (5, 2194): 296.47033149721085, (5, 2195): 296.4150783471402, (5, 2197): 297.09125000620895, (5, 2205): 296.4216546761207, (5, 2207): 295.54510404737715, (5, 2208): 296.0385444494055, (5, 2212): 297.0734521397988, (5, 2214): 287.3718890649959, (5, 2225): 288.59359911368233, (5, 2231): 285.93394841683306, (5, 2278): 293.58222250103785, (5, 2284): 294.61615355307237, (5, 2285): 294.48249112284145, (5, 2291): 292.52175877799476, (5, 2292): 292.67826310620006, (5, 2307): 293.9587479688701, (5, 2313): 292.3025199055518, (5, 2317): 291.9027856995017, (5, 2319): 293.0334563643298, (5, 2321): 293.5095142199463, (5, 2323): 293.4303091829814, (5, 2326): 295.1700062229685, (5, 2327): 294.7308434114898, (5, 2329): 294.4329766860939, (5, 2330): 294.09794533194327, (5, 2332): 294.8299000998801, (5, 2344): 293.68376334333965, (5, 2346): 293.67608349336155, (5, 2361): 293.3940991032798, (5, 2368): 298.58274653185316, (5, 2374): 299.07617005035155, (5, 2375): 299.2314896973784, (5, 2377): 297.5336315232657, (5, 2378): 299.54158071830113, (5, 2379): 299.5968705084806, (5, 2380): 299.7546203375703, (5, 2383): 297.9761563014392, (5, 2385): 298.2323206131497, (5, 2395): 298.249589153941, (5, 2397): 299.4017849609473, (5, 2398): 296.9941201093319, (5, 2399): 297.5959090305367, (5, 2400): 297.4593248371623, (5, 2402): 298.4601461469824, (5, 2403): 298.8386169335503, (5, 2404): 298.9310212267632, (5, 2405): 298.02349741139915, (5, 2407): 298.75537660421674, (5, 2408): 299.2048472533985, (5, 2409): 298.2968319789593, (5, 2411): 298.85613610457233, (5, 2412): 298.7492869812846, (5, 2413): 299.0625185747897, (5, 2414): 298.56050752212235, (5, 2422): 298.7478573568768, (5, 2424): 298.85167965095746, (5, 2426): 298.9295489427262, (5, 2433): 298.2322001061949, (5, 2436): 298.0577161767978, (5, 2437): 295.8450587082371, (5, 2440): 296.3291304021026, (5, 2445): 306.1894888019664, (5, 2447): 304.98085113889465, (5, 2454): 306.1100816993072, (5, 2455): 306.1656156805873, (5, 2460): 302.66860281200974, (5, 2461): 303.10183736982566, (5, 2471): 310.13312347969423, (5, 2492): 302.8768712898003, (5, 2511): 299.36097352961815, (5, 2523): 301.1601984599014, (5, 2525): 300.63615125897303, (5, 2535): 301.4940770317078, (5, 2537): 300.7221866485079, (5, 2538): 301.2519733396631, (5, 2539): 301.03871218243575, (5, 2540): 301.8446001923788, (5, 2542): 302.4081086372301, (5, 2559): 313.37868771333046, (5, 2575): 312.4005340978639, (5, 2599): 295.6967104116237, (5, 2600): 299.44015507024545, (5, 2607): 297.26136795942, (5, 2627): 301.52392393650626, (5, 2647): 303.56740345418297, (5, 2674): 302.5201523802206, (5, 2681): 302.2339712874283, (5, 2683): 303.2335335453999, (5, 2686): 302.0875111651434, (5, 2689): 315.40802993981976, (5, 2690): 315.47208894993474, (5, 2713): 318.0194507840998, (5, 2714): 318.23854986158705, (5, 2715): 318.56643571876356, (5, 2739): 318.2770755134079, (5, 2740): 316.2205177599072, (5, 2741): 316.3843333791277, (5, 2749): 317.8189135666068, (5, 2750): 317.9232707668145, (5, 2752): 318.15791575658005, (5, 2755): 318.41609529121325, (5, 2758): 318.33887417563125, (5, 2759): 318.3408277137585, (5, 2769): 317.961926994938, (5, 2771): 316.7472430193378, (5, 2779): 316.8385817960015, (5, 2784): 313.140189769945, (5, 2800): 313.78688391655646, (5, 2802): 315.5805964807777, (5, 2803): 315.45688923820586, (5, 2804): 315.23807700699496, (5, 2805): 315.85341881112134, (5, 2807): 315.834155228645, (5, 2809): 315.7092581353384, (5, 2812): 313.6065911739328, (5, 2814): 315.5890491131862, (5, 2817): 315.64574817569684, (5, 2819): 315.87974326600937, (5, 2823): 313.79963107964073, (5, 2832): 316.2593362632417, (5, 2836): 314.78166927066553, (5, 2839): 315.8306143729973, (5, 2841): 315.72707689948885, (5, 2843): 315.6200540848271, (5, 2846): 315.0677115663163, (5, 2849): 316.4876022545886, (5, 2852): 316.15292076130453, (5, 2853): 316.6415556481961, (5, 2876): 316.7838679450585, (5, 2877): 317.9679970941433, (5, 2885): 318.30837542000046, (5, 2918): 316.05267924811847, (5, 2921): 316.5620598230248, (5, 2925): 314.17021235607837, (5, 2926): 313.36937274643935, (5, 2930): 315.17151455130875, (5, 2931): 314.39073664702806, (5, 2938): 316.0581983400674, (5, 2940): 317.54285905394954, (5, 2947): 315.8001468581094, (5, 2949): 315.1584818027006, (5, 2950): 315.38710630804275, (5, 2952): 315.13523715391347, (5, 2958): 315.0864544581668, (5, 2959): 315.32996297879555, (5, 2960): 315.890742601058, (5, 2961): 315.6211041629382, (5, 2963): 314.8726626087903, (5, 2968): 315.03244177215515, (5, 2976): 314.80610448085656, (5, 2981): 310.008243224655, (5, 2982): 309.8685966011655, (5, 2984): 309.6190850040781, (5, 3003): 309.17949095146423, (5, 3046): 305.9237751289231, (5, 3050): 308.4878514808565, (5, 3051): 308.6850812614381, (5, 3053): 308.13509409437773, (5, 3069): 311.2069938261454, (5, 3071): 308.002758296808, (5, 3080): 318.3091307231345, (5, 3199): 308.35389147352475, (5, 3200): 307.77201725476124, (5, 3205): 311.3504176055998, (5, 3209): 308.07501719930167, (5, 3215): 307.80891143392347, (5, 3217): 307.0941329938245, (5, 3249): 307.8748950708655, (5, 3263): 313.2720714058322, (5, 3289): 309.58164453697464, (5, 3301): 309.7516410953185, (5, 3302): 309.4947377539036, (5, 3307): 309.17400946261944, (5, 3310): 310.05930998643566, (5, 3391): 310.61389835725953, (5, 3509): 194.49170568078563, (5, 3510): 193.98104199339798, (5, 3511): 194.3202761194088, (5, 3512): 194.00356492821984, (5, 3514): 194.1101189595122, (5, 3519): 195.6931660236147, (5, 3536): 195.39102026381207, (5, 3545): 196.19135756370594, (5, 3548): 195.40688195599003, (5, 3572): 195.6821402042766, (5, 3581): 195.06620851376883, (5, 3583): 194.715070516885, (5, 3601): 196.65325690173324, (5, 3656): 195.82662070937917, (5, 3669): 194.8317459136298, (5, 3670): 195.28985918296348, (5, 3695): 192.67181506645176, (5, 3696): 193.0336110496251, (5, 3782): 195.5633106787301, (5, 3792): 195.00760570105825, (5, 3989): 33.010142819324784, (5, 4008): 35.688495118205445, (5, 4031): 36.64797533738799, (5, 4045): 34.61354233908683, (5, 4144): 33.727388029365244, (5, 4145): 29.908034470747715, (5, 4164): 32.419754105505156, (5, 4168): 31.06189200101174, (5, 4173): 30.637486246643462, (5, 4181): 28.98005107122702, (5, 4228): 28.646685963459863, (5, 4248): 26.332945782648657, (5, 4254): 12.5, (5, 4260): 12.5, (5, 4262): 12.5, (5, 4273): 12.5, (5, 4319): 12.5, (5, 4326): 12.5, (5, 4328): 12.5, (5, 4334): 12.5, (5, 4335): 12.5, (5, 4372): 90.01685837236029, (5, 4413): 95.61770126905438, (5, 4434): 89.27321575643404, (5, 4447): 87.799530203978, (5, 4452): 89.61154241708508, (5, 4463): 97.07831640246516, (5, 4465): 96.44809725280808, (5, 4619): 101.90352331795403, (5, 4645): 101.28157354416483, (5, 4657): 101.96873244868257, (5, 4666): 102.51185452296743, (5, 4676): 102.69709229050285, (5, 4678): 102.39394307925457, (5, 4689): 103.13239241176036, (5, 4704): 104.37416094887016, (5, 4726): 123.77689749839026, (5, 4727): 123.4763348666715, (5, 4730): 122.84764600155455, (5, 4731): 123.33502475415277, (5, 4734): 121.90680236551728, (5, 4735): 121.8866226739434, (5, 4736): 122.2600048893906, (5, 4737): 122.068021840131, (5, 4738): 122.32102639292832, (5, 4756): 122.76190459057764, (5, 4760): 119.96329094975631, (5, 4761): 119.61118618736853, (5, 4762): 119.87153627571017, (5, 4765): 120.2662927999562, (5, 4773): 124.11344409175047, (5, 4774): 124.26674240126206, (5, 4790): 123.85024381931295, (5, 4795): 123.48183398543269, (5, 4799): 124.61986468968728, (5, 4801): 125.82516820266838, (5, 4804): 123.05582018901642, (5, 4805): 122.75912372475875, (5, 4806): 124.77417696869118, (5, 4815): 124.85766103504216, (5, 4816): 125.41726498386888, (5, 4817): 126.05003705061435, (5, 4826): 125.45376614700793, (5, 4830): 125.23517932914248, (5, 4839): 120.85877403039999, (5, 4840): 121.33595094657359, (5, 4841): 120.87629815236781, (5, 4846): 120.58648492013842, (5, 4848): 120.94190038033943, (5, 4850): 121.28501118654036, (5, 4871): 115.89547736090714, (5, 4883): 119.00986730774753, (5, 4900): 116.80683920518365, (5, 4901): 116.77804340085832, (5, 4917): 110.38684480736521, (5, 4931): 109.06615747448808, (5, 4944): 110.216547846881, (5, 4956): 109.62785571218197, (5, 4958): 110.2272105700837, (5, 4959): 110.41665101637875, (5, 4961): 109.63315528904452, (5, 4966): 109.67896085443925, (5, 5207): 108.33136288732544, (5, 5272): 71.97948506601918, (5, 5283): 72.23877227825805, (5, 5287): 74.20054950174521, (5, 5289): 74.38633293519003, (5, 5293): 70.54798291898017, (5, 5295): 71.07347432347822, (5, 5296): 71.9995948315337, (5, 5298): 72.51159953016365, (5, 5303): 73.48726529763343, (5, 5305): 73.66287666860924, (5, 5306): 74.82705866075266, (5, 5307): 73.64774804392162, (5, 5308): 74.04929712368696, (5, 5313): 72.87733866113071, (5, 5314): 72.64653495004653, (5, 5317): 74.65343284258657, (5, 5319): 73.50313552901433, (5, 5324): 72.67438965323882, (5, 5326): 72.09056999024477, (5, 5348): 75.57742503903968, (5, 5351): 77.00797326107161, (5, 5399): 75.87707280686965, (5, 5413): 79.31762334587226, (5, 5422): 75.07131636703373, (5, 5445): 74.99557807560248, (5, 5448): 74.82353005350967, (5, 5456): 75.76577925215955, (5, 5467): 76.188317444099, (5, 5624): 71.83664573308837, (5, 5671): 65.65502075584261, (5, 5672): 65.04667298397908, (5, 5797): 73.45343321373898, (5, 5871): 88.56770808468022, (5, 5976): 85.6430871970987, (5, 6118): 256.3550247779906, (5, 6248): 267.3676548044337, (5, 6345): 81.07259277092948, (5, 6352): 83.6112919433385, (5, 6354): 80.4019735900211, (5, 6359): 79.99132728920296, (5, 6376): 83.44821466761549, (5, 6378): 80.71271681718842, (5, 6381): 80.26334964150296, (5, 6383): 81.57411052074339, (5, 6396): 80.94681437677549, (5, 6399): 81.15319228285416, (5, 6408): 83.42590941226021, (5, 6409): 82.00350013513382, (5, 6419): 85.73949383286502, (5, 6422): 82.90831857981739, (5, 6423): 83.09969613496656, (5, 6424): 80.39574300939479, (5, 6439): 80.81019239046014, (5, 6464): 81.44178907446313, (5, 6465): 81.76633337826928, (5, 6469): 81.61323627529069, (5, 6470): 81.80691167727736, (5, 6472): 79.16734528279213, (5, 6480): 79.31191144595236, (5, 6486): 77.47470979275916, (5, 6497): 78.06514584125283, (5, 6503): 80.88412893339165, (5, 6508): 80.91057264919309, (5, 6509): 80.33148594805799, (5, 6521): 78.84161663952938, (5, 6544): 78.81066626139085, (5, 6552): 82.09315383760749, (5, 6553): 82.46092346758228, (5, 6554): 82.8379198472461, (5, 6578): 81.50957654270643, (5, 6582): 81.57418021384359, (5, 6601): 81.29362457042019, (5, 6609): 78.52869804196115, (5, 6610): 78.36944947828893, (5, 6611): 78.43245742355298, (5, 6614): 78.7141589616175, (5, 6615): 78.59438060338837, (5, 6616): 78.0214636170188, (5, 6617): 78.255894554369, (5, 6618): 77.52568293448603, (5, 6619): 78.9591045013172, (5, 6620): 77.93160619729527, (5, 6621): 78.23648787282973, (5, 6622): 78.21722098405989, (5, 6623): 78.6516715955701, (5, 6624): 78.8479543677342, (5, 6625): 78.95426409218945, (5, 6626): 79.01639078029234, (5, 6627): 78.87326790512847, (5, 6628): 77.9178525881869, (5, 6629): 78.65698538642829, (5, 6630): 79.37215927676597, (5, 6632): 78.73538540264119, (5, 6634): 79.66241234896489, (5, 6635): 78.39552687134568, (5, 6636): 77.97475745940675, (5, 6637): 79.08948592153467, (5, 6638): 79.24809240053398, (5, 6639): 78.78636011040142, (5, 6640): 79.23869959548523, (5, 6641): 78.18313151844367, (5, 6642): 79.18277986622624, (5, 6643): 79.11808312575043, (5, 6645): 78.8737095515734, (5, 6646): 77.7045849968863, (5, 6647): 79.11780106201559, (5, 6653): 78.6364335674633, (5, 6655): 78.81243474001838, (5, 6658): 79.65188740929602, (5, 6662): 79.14056959490676, (5, 6819): 96.60575319030113, (5, 6996): 89.88493166524951, (5, 7059): 85.63584263377886, (5, 7187): 93.83905969424858, (5, 7304): 101.92726125631795, (5, 7528): 90.29898671123956, (5, 7720): 65.04480906600963, (5, 7793): 65.64257736868952, (5, 7807): 65.25976055653597, (5, 7808): 65.80218758597444, (5, 7831): 75.6672677081879, (5, 7850): 71.97098599680662, (5, 7852): 73.02119891064612, (5, 8012): 66.32922956128475, (5, 8125): 64.86074355214299, (5, 8208): 57.310079662251404, (5, 8392): 71.89409883404016, (5, 8651): 117.04085504143538, (5, 9088): 99.50891660418534, (5, 9443): 126.77043887460205, (5, 9444): 126.2084050263724, (5, 9828): 146.36123730114593, (5, 9868): 145.81878175853038, (5, 10180): 64.84476009136226, (5, 10256): 55.527054859542694, (5, 10276): 58.98603705955935, (5, 10378): 55.83556011232369, (5, 10676): 72.21129381982135, (5, 10714): 79.55708453578055, (5, 10730): 75.25654090679524, (5, 10862): 130.06969602470366, (5, 10881): 129.68793229293436, (5, 10883): 129.98686687292724, (5, 10885): 130.08961466210724, (5, 10891): 130.45778701611516, (5, 10909): 129.87832605042863, (5, 10911): 129.1959556267084, (5, 10913): 129.48711668137344, (5, 10915): 129.16709846426284, (5, 10919): 128.8414448592592, (5, 11037): 139.2660447217135, (5, 11039): 137.80429984614608, (5, 11516): 71.85143598643637, (5, 11856): 12.5, (5, 11857): 12.5, (5, 11861): 12.5, (5, 11881): 12.5, (5, 11902): 12.5, (5, 11911): 12.5, (5, 11914): 12.5, (5, 11922): 12.5, (5, 11924): 12.5, (5, 11926): 12.5, (5, 11950): 12.5, (5, 11963): 12.5, (5, 11983): 12.5, (5, 11985): 12.5, (5, 12009): 12.5, (5, 12010): 12.5, (5, 12018): 12.5, (5, 12020): 12.5, (5, 12021): 12.5, (5, 12024): 12.5, (5, 12025): 12.5, (5, 12027): 12.5, (5, 12031): 12.5, (5, 12032): 12.5, (5, 12035): 12.5, (5, 12041): 12.5, (5, 12045): 15.54496214075134, (5, 12145): 12.5, (5, 12275): 36.5914880071638, (5, 12294): 36.39305871613977, (5, 12358): 43.87311948291256, (5, 12463): 47.95186771241706, (5, 12465): 47.960341481184194, (5, 12482): 47.86787528425188, (5, 12503): 48.01096517298648, (5, 12506): 48.30164092090032, (5, 12549): 46.22366314055559, (5, 12559): 46.28512039638357, (5, 12569): 47.03884974748904, (5, 12572): 47.228989013968246, (5, 12574): 46.67234657113812, (5, 12576): 46.312179580669856, (5, 12591): 45.456435173208085, (5, 12608): 46.795860319827234, (5, 12696): 43.24895838846169, (5, 12710): 44.040423142915735, (5, 12728): 44.216192624394836, (5, 12766): 51.462959740029866, (5, 12771): 51.52082428490179, (5, 12790): 51.97992721243107, (5, 12795): 53.33570444236269, (5, 12797): 55.55516528747914, (5, 12798): 54.96991477721762, (5, 12811): 52.215743175396476, (5, 12830): 53.5496009915977, (5, 12848): 52.223128240694095, (5, 12850): 51.491910659614696, (5, 12852): 53.4243374377531, (5, 12854): 53.85277106208008, (5, 12859): 51.575065682913475, (5, 12861): 54.306893459380355, (5, 12865): 52.086030921966824, (5, 12866): 52.041523473508526, (5, 12867): 51.441150394865524, (5, 12874): 51.766241805182595, (5, 12875): 51.338299399594696, (5, 12881): 52.93582604633953, (5, 12883): 52.38714229906414, (5, 12885): 51.12569211571725, (5, 12888): 52.45684233587834, (5, 12889): 52.407754223366915, (5, 12892): 51.7781293510398, (5, 12893): 52.6153287012987, (5, 12896): 52.18393353718168, (5, 12906): 52.55298067163017, (5, 13018): 61.23797919397552, (5, 13071): 62.38101898219498, (5, 13131): 61.38190939305517, (5, 13146): 57.65190066952783, (5, 13159): 67.0143732099519, (5, 13193): 61.671196658705945, (5, 13198): 65.59411049760139, (5, 13292): 58.929704805717506, (5, 13296): 55.66825054214425, (5, 13406): 71.28086709666347, (5, 13407): 71.6479320851818, (5, 13417): 73.6108236961555, (5, 13418): 73.303250240659, (5, 13438): 69.69930676419283, (5, 13442): 68.70124762286005, (5, 13443): 69.22294076221364, (5, 13764): 120.77318587940837, (5, 13766): 120.13346514930558, (5, 13771): 121.29896987812708, (5, 13783): 120.42513678813698, (5, 13784): 119.20355998567636, (5, 13792): 123.3539626292748, (5, 13824): 120.97064283329553, (5, 14017): 114.25287983910046, (5, 14870): 117.13971108384791, (5, 14997): 97.08830321660334, (5, 15000): 97.05989169462111, (5, 15003): 96.65690576202294, (5, 15006): 95.50307531729754, (5, 15007): 95.05504974970408, (5, 15056): 95.21654564265309, (5, 15063): 95.64181947425496, (5, 15069): 95.84190952831513, (5, 15076): 95.00508048572425, (5, 15086): 96.38479027769402, (5, 15087): 96.90971715912147, (5, 15111): 98.23693025281929, (5, 15116): 97.47678226085905, (5, 15722): 109.4338659382585, (5, 15998): 118.85609713820232, (5, 16073): 217.2630060753452, (5, 16939): 272.081676715031, (5, 16940): 271.4156560837702, (5, 16951): 272.1901947654929, (5, 16963): 272.25023436810994, (5, 16965): 273.0535490469116, (5, 16969): 272.8669756088673, (5, 16970): 272.53787927484944, (5, 16971): 271.8134825036451, (5, 16973): 271.77078884494443, (5, 16974): 273.3821509424211, (5, 16976): 272.5902198700274, (5, 16978): 272.0588792484325, (5, 16980): 272.85272781988084, (5, 16982): 273.38263544666694, (5, 17045): 295.8559818210446, (5, 17048): 296.7943329713187, (5, 17304): 21.10724364198864, (5, 17305): 21.50392616686606, (5, 17330): 21.615405003200426, (5, 17334): 20.215855277434393, (5, 17343): 22.330916492253316, (5, 17345): 21.017077580087523, (5, 17347): 22.107148632470835, (5, 17351): 19.207749683524014, (5, 17372): 20.441203686907347, (5, 17373): 22.163739282761526, (5, 17377): 22.3508701277397, (5, 17382): 21.403044586842626, (5, 17383): 21.304579940940254, (5, 17389): 20.811690460361785, (5, 17400): 21.64637933706652, (5, 17401): 21.501445781121927, (5, 17402): 21.77994543862159, (5, 17403): 21.940125719279866, (5, 17440): 22.015813760982713, (5, 17455): 22.70962346018028, (5, 17491): 23.427469387080578, (5, 17507): 17.894959211580854, (5, 17509): 18.257525646488922, (5, 17590): 19.85797305734263, (5, 17615): 12.5, (5, 17642): 12.962847693269794, (5, 17643): 13.151760122776064, (5, 17668): 12.5, (5, 17721): 12.5, (5, 17754): 15.158190301993587, (5, 17769): 17.335619689597237, (5, 17776): 16.527769635299922, (5, 17804): 18.12112635398993, (5, 17809): 18.67268885332997, (5, 17824): 17.971713611565466, (5, 17837): 18.324006323881566, (5, 17838): 18.816632940741577, (5, 17862): 18.666995282637597, (5, 17866): 19.510528340322686, (5, 17872): 18.03706128505221, (5, 17873): 17.530913349492366, (5, 17881): 18.390660808310813, (5, 17947): 217.0750842099801, (5, 17951): 215.85108777610486, (5, 17953): 215.59334219326556, (5, 17954): 215.66333315397574, (5, 17959): 216.86459695238062, (5, 17963): 216.47457466630442, (5, 18000): 210.1802717605307, (5, 18001): 210.3940317763807, (5, 18111): 226.90362027220496, (5, 18148): 195.14701586135746, (5, 18166): 207.31914763787643, (5, 18189): 218.91187543894992, (5, 18239): 22.11753888210784, (5, 18240): 22.196858987664577, (5, 18245): 22.208604948695655, (5, 18247): 22.190031328328352, (5, 18251): 22.310794038004165, (5, 18256): 22.541933217247525, (5, 18258): 22.46666754752746, (5, 18259): 22.536081941723978, (5, 18260): 22.65031858839797, (5, 18262): 22.80321744116471, (5, 18263): 22.62403118520732, (5, 18264): 22.73175721690993, (5, 18266): 22.918245651061923, (5, 18267): 23.01182671060016, (5, 18268): 23.09080307699945, (5, 18269): 23.286991447686596, (5, 18275): 23.194805958265782, (5, 18285): 22.660985659320332, (5, 18308): 20.630870210240055, (5, 18313): 20.17988939930177, (5, 18314): 20.645802808009655, (5, 18315): 23.03393282892145, (5, 18316): 23.137823142501592, (5, 18317): 23.236857016568184, (5, 18320): 23.16002317402819, (5, 18321): 23.267198835454828, (5, 18322): 23.39921966156585, (5, 18324): 23.33980848681193, (5, 18325): 23.588102046726497, (5, 18326): 23.490214626336538, (5, 18327): 23.42671702490501, (5, 18329): 23.57131670965226, (5, 18330): 23.808271890435716, (5, 18331): 23.584914920938964, (5, 18332): 23.41568263211687, (5, 18333): 23.678161697590223, (5, 18336): 23.364873648279577, (5, 18337): 23.37567555012014, (5, 18403): 23.91241288412183, (5, 18432): 24.689664056320076, (5, 18451): 24.05226421985447, (5, 18466): 23.66535399404857, (5, 18481): 22.792788726971857, (5, 18483): 22.873685939822593, (5, 18484): 22.674274740090823, (5, 18485): 21.99227792457697, (5, 18486): 22.080373288828568, (5, 18487): 21.662879052100767, (5, 18489): 22.309471048157924, (5, 18490): 22.416551946533215, (5, 18491): 22.56840071364854, (5, 18492): 21.404701574647977, (5, 18493): 21.933382800655686, (5, 18494): 22.313086921124935, (5, 18495): 22.291742069499218, (5, 18496): 22.197278519174247, (5, 18497): 21.494699688111155, (5, 18498): 21.888869507857642, (5, 18499): 22.15425847178685, (5, 18501): 21.822288857921027, (5, 18502): 21.643220016321088, (5, 18503): 21.60226510700972, (5, 18504): 22.357552560308534, (5, 18506): 21.623568875677158, (5, 18507): 21.408783398245447, (5, 18508): 22.040383587547154, (5, 18509): 21.969030291962554, (5, 18510): 21.49594840463355, (5, 18511): 21.827069730507574, (5, 18512): 21.77342506031695, (5, 18515): 22.26119676023986, (5, 18516): 22.018277981905104, (5, 18517): 21.68202452514702, (5, 18518): 22.22591084757386, (5, 18519): 22.439930748656398, (5, 18520): 22.08528336381461, (5, 18522): 23.305711128439455, (5, 18523): 23.253147686800865, (5, 18532): 23.35486576348465, (5, 18535): 23.0556380714486, (5, 18537): 22.891105771789405, (5, 18539): 22.879320168917918, (5, 18540): 22.850014223202596, (5, 18541): 22.89184380520993, (5, 18542): 22.92711060846098, (5, 18543): 22.71858974883868, (5, 18546): 22.669286534098838, (5, 18555): 22.925396017863644, (5, 18556): 22.914893496122698, (5, 18565): 23.2199556070359, (5, 18567): 23.129805611806436, (5, 18568): 23.059074476262595, (5, 18577): 24.130584588407753, (5, 18583): 24.170859668459293, (5, 18605): 24.66846326285404, (5, 18608): 22.892620418494126, (5, 18616): 25.66796050979022, (5, 18618): 26.421086986418608, (5, 18625): 26.673054873519675, (5, 18645): 26.163969333868685, (5, 18646): 26.158794644022, (5, 18653): 24.878989626094068, (5, 18654): 25.552702726775955, (5, 18655): 24.988379671524033, (5, 18666): 28.808194004288435, (5, 18837): 37.03600976346359, (5, 18974): 26.50689585767859, (5, 18999): 28.3782754546924, (5, 19000): 28.5897947248504, (5, 19174): 32.501433500632764, (5, 19342): 35.989064135348876, (5, 19455): 25.78090053238548, (5, 19555): 34.25302598738063, (5, 19564): 37.40957902425852, (5, 19573): 36.9311615206577, (5, 19586): 36.49478333679504, (5, 19605): 35.80307684996398, (5, 19611): 35.97402961958084, (5, 19614): 34.91609503137005, (5, 19641): 34.42884028318315, (5, 19702): 35.640267206524456, (5, 19713): 35.342163494752555, (5, 19731): 30.7950638550711, (5, 19819): 28.254013216170186, (5, 19893): 38.060893490181776, (5, 19899): 39.83140763028928, (5, 19929): 37.62835129770732, (5, 19951): 38.855117043403226, (5, 19962): 39.23311692308532, (5, 19970): 36.09060405318497, (5, 19971): 36.8506016298218, (5, 19972): 37.35532161770482, (5, 19975): 36.812377494198124, (5, 19978): 35.70314871411498, (5, 19987): 35.199927684348935, (5, 19989): 34.64223260304239, (5, 20039): 35.05559043893736, (5, 20043): 34.59038299975515, (5, 20047): 33.702509464015016, (5, 20052): 33.68038704259839, (5, 20054): 34.07302025620129, (5, 20085): 33.38094684596799, (5, 20104): 33.60622858323274, (5, 20132): 33.22637082474596, (5, 20203): 44.86648232773083, (5, 20280): 47.07221582766978, (5, 20285): 48.00071742359193, (5, 20290): 46.64124402587696, (5, 20297): 46.47603955505411, (5, 20309): 41.59708399489078, (5, 20453): 41.014248743698985, (5, 20485): 46.07383525017202, (5, 20520): 45.945389520456786, (5, 20526): 48.16866547287182, (5, 20698): 147.93644093464005, (5, 20868): 171.08447391385036, (5, 21042): 45.407599835712574, (5, 21057): 40.727356066691954, (5, 21066): 42.937884347509275, (5, 21075): 43.9364857144162, (5, 21093): 44.972780740273656, (5, 21098): 41.54603121393571, (5, 21127): 44.97107717772083, (5, 21130): 44.04335744880809, (5, 21144): 44.25840934315446, (5, 21146): 45.28037398513527, (5, 21147): 44.36982093181531, (5, 21148): 43.5158013748596, (5, 21153): 46.1509843311287, (5, 21293): 37.478540065783456, (5, 21426): 41.866277952249504, (5, 21442): 38.9006735920111, (5, 21451): 38.62236950291238, (5, 21466): 39.984505954187306, (5, 21469): 39.24366418382285, (5, 21471): 40.37322878919112, (5, 21473): 39.68908507062427, (5, 21475): 40.222818846571286, (5, 21482): 39.02099337248531, (5, 21484): 39.04497006549311, (5, 21488): 39.544521222698314, (5, 21494): 39.907109475335986, (5, 21498): 39.43273037629626, (5, 21500): 39.942616060237704, (5, 21514): 37.499854761642865, (5, 21537): 39.449192141470874, (5, 21662): 36.2137735328254, (5, 21691): 39.014964294110555, (5, 21757): 45.795675183769674, (5, 21777): 54.65123590467187, (5, 21778): 55.396586123057716, (5, 21779): 55.034316515843365, (5, 21790): 53.76361931315234, (5, 21802): 53.898891728705216, (5, 21824): 53.18800153774099, (5, 21874): 54.920519980533435, (5, 21879): 55.503508532270544, (5, 21983): 51.95652481797787, (5, 22002): 44.09175648053848, (5, 22132): 50.54956441399449, (5, 22261): 153.7254480870847, (5, 22298): 152.2984992185864, (5, 22339): 161.4454908093638, (5, 22508): 138.89697815641983, (5, 22841): 306.6503741031811, (5, 22842): 306.68204738332736, (5, 22874): 304.9628734976777, (5, 22941): 305.05397825919874, (5, 22956): 306.18645028975084, (5, 22960): 306.4461791364606, (5, 22968): 307.9101079319235, (5, 22970): 308.1625602136742, (5, 22974): 308.93049106752056, (5, 22980): 310.2644551741868, (5, 23025): 310.42840044538605, (5, 23028): 310.1894837057637, (5, 23081): 312.76900758825855, (5, 23104): 310.78031087332783, (5, 23147): 298.2677295190227, (5, 23298): 24.209035403095182, (5, 23376): 26.039941097592582, (5, 23381): 26.22325554421946, (5, 23529): 22.018849770449226, (5, 23556): 23.25760060028478, (5, 23718): 26.499333133731067, (5, 24001): 15.859029056592666, (5, 24094): 12.5, (5, 24129): 12.5, (5, 24174): 12.5, (5, 24235): 12.5, (5, 24259): 12.5, (5, 24260): 12.5, (5, 24261): 12.5, (5, 24305): 12.5, (5, 24306): 12.5, (5, 24307): 12.5, (5, 24308): 17.905434144190842, (5, 24498): 14.117428222960227, (5, 24499): 14.050291236950265, (5, 24500): 13.918149616402443, (5, 24668): 18.12196113791889, (5, 24711): 13.928263349382627, (5, 24756): 13.74151249415445, (5, 24788): 14.78636228821557, (5, 24809): 12.5, (5, 24813): 12.640071241667291, (5, 24821): 12.5, (5, 24825): 12.5, (5, 24832): 12.5, (5, 24833): 12.5, (5, 24835): 12.5, (5, 24837): 12.911126945856457, (5, 24840): 12.5, (5, 24841): 12.5, (5, 24844): 12.5, (5, 24845): 12.5, (5, 24846): 12.5, (5, 24849): 12.5, (5, 24850): 12.634544938605794, (5, 24863): 12.5, (5, 24866): 12.5, (5, 24885): 12.5, (5, 24886): 12.5, (5, 24889): 12.5, (5, 24903): 12.5, (5, 24909): 12.5, (5, 24999): 42.42797043089185, (5, 25019): 42.43453003179121, (5, 25028): 41.845033156188606, (5, 25137): 56.32456262810331, (5, 25145): 55.944786442570745, (5, 25208): 61.369288114267285, (5, 25233): 61.940790901037104, (5, 25371): 50.69838518021687, (5, 25377): 50.179870290014826, (5, 25828): 76.76060866907878, (5, 25851): 80.00253196862924, (5, 25874): 75.52078600229738, (5, 25898): 75.48414265962002, (5, 25946): 77.15515700449417, (5, 26047): 71.84331853433416, (5, 26066): 48.55617381738095, (5, 26197): 61.54329032039433, (5, 26212): 100.75441833683362, (5, 26253): 103.1582491362455, (5, 26254): 102.10099525224753, (5, 26257): 101.71490651244001, (5, 26258): 102.80675829329107, (5, 26260): 102.2110653361404, (5, 26266): 102.10627808036489, (5, 26267): 101.55453600574295, (5, 26271): 101.65536539497775, (5, 26304): 92.75118725977013, (5, 26305): 92.50404961255987, (5, 26363): 81.12926816400812, (5, 26441): 156.8818157495438, (5, 26442): 156.66819430125284, (5, 26450): 155.46028471099766, (5, 26459): 155.2295897856929, (5, 26462): 155.33863877356902, (5, 26467): 158.8596601050551, (5, 26471): 157.94061951477187, (5, 26472): 157.85603646978612, (5, 26473): 157.83485184833262, (5, 26476): 157.47310000925134, (5, 26485): 155.89486393897604, (5, 26493): 156.00189286222965, (5, 26524): 155.80696074771714, (5, 26525): 155.7055116011678, (5, 26556): 157.4579770611335, (5, 26560): 157.22944000015764, (5, 26561): 156.44233030901785, (5, 26564): 157.16394658314738, (5, 26569): 156.29397875672967, (5, 26570): 156.03401427537543, (5, 26573): 156.28917761289227, (5, 26581): 156.31749255689778, (5, 26583): 156.01976790015894, (5, 26593): 156.39740854275323, (5, 26837): 159.15487009880792, (5, 26844): 159.93305626371122, (5, 26863): 158.37700155060156, (5, 26893): 160.67173469320923, (5, 26902): 161.732938932211, (5, 26905): 160.53592171695385, (5, 26912): 161.40340908015702, (5, 26921): 159.46761495466342, (5, 26922): 157.54332270817218, (5, 27212): 161.9618314489708, (5, 27218): 160.89004350879583, (5, 27239): 163.5245476600073, (5, 27257): 162.75958844565915, (5, 27274): 163.85785105019775, (5, 27279): 163.7259863710801, (5, 27282): 162.81677228402728, (5, 27283): 163.09876980697572, (5, 27285): 164.2932708792063, (5, 27286): 163.52929610034462, (5, 27290): 162.04615855149476, (5, 27295): 161.42652913188235, (5, 27300): 163.99909921571577, (5, 27344): 161.74520614144546, (5, 27366): 162.81331021184468, (5, 27383): 164.45558149740415, (5, 27398): 165.46843847794415, (5, 27406): 164.53533262583977, (5, 27407): 164.77243464372185, (5, 27426): 163.31493939515366, (5, 27432): 159.4603881068347, (5, 27460): 161.8384536281645, (5, 27523): 163.75784767971012, (5, 27545): 179.16209778270667, (5, 27602): 200.14209027939768, (5, 27606): 200.4753971873382, (5, 27646): 179.55605559151343, (5, 27667): 183.72264951261792, (5, 27672): 183.91035118797842, (5, 27674): 183.21918796338605, (5, 27688): 183.6929306663098, (5, 27692): 184.66628285694787, (5, 27693): 184.04896764366035, (5, 27705): 184.05128226912495, (5, 27712): 184.38440387412848, (5, 27786): 199.8160322086598, (5, 27790): 197.0057437326935, (5, 27791): 196.74089625103338, (5, 27795): 198.6831933740876, (5, 27801): 196.6318711075224, (5, 27813): 200.511680483632, (5, 27816): 199.65930916173417, (5, 27823): 196.54993828651132, (5, 27830): 198.63140801924513, (5, 27884): 172.97911116261068, (5, 27885): 177.86250886659406, (5, 27896): 174.88991605715117, (5, 27919): 174.6511042961513, (5, 27922): 175.31076602883226, (5, 27930): 173.6755038385956, (5, 27934): 173.8938967613242, (5, 27935): 174.06790299107433, (5, 27948): 199.55858002388305, (5, 27951): 200.2059936279776, (5, 28061): 183.41821351892537, (5, 28290): 225.97739264070017, (5, 28292): 226.9023194477751, (5, 28293): 226.16115076889423, (5, 28295): 225.81807097157179, (5, 28296): 225.94754274701143, (5, 28297): 225.48849228224316, (5, 28302): 225.20167038855087, (5, 28310): 240.6067575645344, (5, 28313): 241.21857663416776, (5, 28372): 241.46294324884417, (5, 28398): 241.52427333393976, (5, 28399): 241.22998116018854, (5, 28400): 241.6916928877283, (5, 28401): 240.49483588292767, (5, 28445): 240.7535101916204, (5, 28475): 239.64711955565645, (5, 28885): 12.5, (5, 28886): 12.5, (5, 28915): 12.5, (5, 28916): 12.5, (5, 28917): 12.5, (5, 28921): 12.5, (5, 28931): 12.5, (5, 28945): 12.5, (5, 28982): 12.5, (5, 29219): 16.430708423665923, (5, 29228): 16.515176434703445, (5, 29246): 23.033334542928362, (5, 29248): 24.430908589260696, (5, 29282): 22.965383525031044, (5, 29290): 22.20510034817503, (5, 29291): 22.321780894856353, (5, 29292): 22.41571375759498, (5, 29293): 21.825594525372125, (5, 29294): 22.89885431809838, (5, 29298): 22.249985650158152, (5, 29299): 22.589415438258516, (5, 29304): 21.20754913499065, (5, 29317): 19.459269295457577, (5, 29323): 19.285564952800353, (5, 29330): 20.169472599537368, (5, 29331): 20.293511179148563, (5, 29344): 19.54536995121075, (5, 29445): 32.47133624197017, (5, 29724): 301.9445445027669, (5, 29738): 302.3033794114079, (5, 29745): 301.1905035486676, (5, 29748): 301.0603433213773, (5, 29750): 301.50399514357395, (5, 29759): 300.60984319326246, (5, 29772): 301.93077669160056, (5, 29781): 301.632670268166, (5, 29784): 301.5512591682227, (5, 29790): 301.860678491479, (5, 29811): 300.9581011657608, (5, 29817): 302.5023435549886, (5, 29818): 302.20580219240884, (5, 29929): 301.27324504544356, (5, 30039): 306.84985524885457, (5, 30066): 304.3349535927385, (5, 30116): 291.45678474952587, (5, 30238): 272.38559014292514, (5, 30248): 282.6922243380033, (5, 30260): 282.9835516489507, (5, 30545): 12.5, (5, 30733): 28.88210800933412, (5, 30756): 34.08259571969508, (5, 30921): 24.499321271939404, (5, 31079): 84.41102337781903, (5, 31149): 83.15263451186786, (5, 31154): 83.6226661954703, (5, 31160): 83.20360529245524, (5, 31163): 83.85596113384425, (5, 31189): 89.2254080015942, (5, 31215): 89.30254849844918, (5, 31259): 92.18777211631965, (5, 31262): 92.64021791219734, (5, 31430): 85.66812470563646, (5, 31568): 105.71715147285038, (5, 31751): 88.70171187218703, (6, 109): 44.52802285325762, (6, 872): 160.25559096105323, (6, 873): 161.17620277957965, (6, 877): 161.0449408099088, (6, 879): 161.2023284263029, (6, 884): 160.75863720701807, (6, 889): 161.23266342441187, (6, 891): 160.39681316421283, (6, 892): 161.87164457263958, (6, 894): 161.66779690268274, (6, 896): 160.42533957946998, (6, 903): 161.32436634295098, (6, 909): 159.0544688197966, (6, 910): 159.22421493287476, (6, 912): 158.66248341381953, (6, 913): 158.11718487461394, (6, 916): 157.59553229917998, (6, 926): 159.26544383017512, (6, 927): 158.9121059373899, (6, 948): 160.02905136534642, (6, 961): 159.6965632706702, (6, 962): 159.6624676403972, (6, 963): 159.668942748952, (6, 967): 161.62628934054786, (6, 974): 161.63393917293763, (6, 998): 162.16669258055626, (6, 1014): 179.88163056789045, (6, 1086): 152.27037858547686, (6, 1087): 151.4596276852589, (6, 1089): 150.9769482644364, (6, 1090): 151.4206092764446, (6, 1092): 152.74483227920095, (6, 1097): 151.8719908906854, (6, 1107): 152.96621647541332, (6, 1387): 42.35130900019202, (6, 1554): 48.31569533295862, (6, 1827): 206.96038967018825, (6, 1828): 206.96730459624317, (6, 1829): 207.1731503750695, (6, 1830): 207.45859699098062, (6, 1831): 207.46504159744273, (6, 1832): 207.322717428766, (6, 1833): 207.259619224568, (6, 1836): 207.0683465771652, (6, 1841): 207.7756900473665, (6, 1843): 207.5250903120795, (6, 1844): 207.71038951018124, (6, 1845): 207.4769040279433, (6, 1847): 206.29312396100948, (6, 1848): 206.65245605079124, (6, 1849): 208.41007333082942, (6, 1850): 208.51790168556073, (6, 1851): 207.12521456786243, (6, 1852): 207.322555737102, (6, 1854): 207.358879069488, (6, 1856): 206.46936831181998, (6, 1857): 206.7216410250861, (6, 1858): 208.1276667070174, (6, 1861): 207.29829246827086, (6, 1866): 206.59512116010683, (6, 1867): 207.64836654501187, (6, 1868): 207.30700341487662, (6, 1870): 207.90378577205166, (6, 1871): 207.45865950564857, (6, 1875): 207.2249920303232, (6, 1880): 206.5379061833313, (6, 1882): 206.8875359095928, (6, 1883): 208.33666849224832, (6, 1889): 206.43414493627267, (6, 1893): 206.91182953101435, (6, 1894): 206.6228439803916, (6, 1899): 206.10491770282155, (6, 1900): 206.22326233533235, (6, 1902): 207.32846781227082, (6, 1905): 207.75023702602024, (6, 1907): 206.71113499089935, (6, 1910): 206.6134119130469, (6, 1917): 207.84363024765838, (6, 1920): 206.5831746609356, (6, 1935): 207.46337696531026, (6, 1937): 207.7833785579445, (6, 1946): 205.1840547492411, (6, 1949): 205.3857721825096, (6, 1950): 204.8045204452193, (6, 1951): 205.17949094956987, (6, 1952): 205.98969753203016, (6, 1953): 205.73758140547838, (6, 1954): 205.80842297089566, (6, 1958): 205.48917167484473, (6, 1960): 206.08889541144524, (6, 1968): 206.32452191034324, (6, 1969): 207.19112528945186, (6, 1974): 206.99418685018813, (6, 1975): 207.10211320909718, (6, 1979): 206.20223644022292, (6, 1980): 206.4834469165139, (6, 1981): 206.47133966700906, (6, 1985): 206.54176229727355, (6, 1994): 205.18980199907924, (6, 2011): 206.98995879124885, (6, 2019): 209.85171271992542, (6, 2020): 209.47588613589468, (6, 2029): 208.37601433272795, (6, 2030): 209.2101160536094, (6, 2032): 208.36562671923224, (6, 2033): 208.78412162520348, (6, 2034): 208.93905831035443, (6, 2036): 208.47167992378203, (6, 2037): 208.56437620930663, (6, 2038): 207.88688145013953, (6, 2042): 211.69095618284487, (6, 2050): 208.37226342062263, (6, 2051): 208.4958017940019, (6, 2053): 208.51837979445023, (6, 2054): 208.8609404367379, (6, 2066): 208.19525978162594, (6, 2067): 208.1060782871082, (6, 2071): 204.46922905387237, (6, 2072): 204.95600328898612, (6, 2073): 202.80017307788768, (6, 2074): 202.8301218362204, (6, 2080): 202.0755111156015, (6, 2082): 205.25867922525828, (6, 2083): 205.49979972362615, (6, 2089): 204.70277099070313, (6, 2090): 204.89740650039346, (6, 2092): 204.39718136461775, (6, 2098): 202.24216911231278, (6, 2099): 202.70282797159425, (6, 2101): 202.33496459143348, (6, 2102): 203.78780980712807, (6, 2103): 203.39469681960904, (6, 2104): 203.25417832583713, (6, 2106): 205.78149108866836, (6, 2112): 202.6747782422786, (6, 2113): 204.09154773598706, (6, 2114): 204.71435251623151, (6, 2117): 206.13984989196976, (6, 2123): 197.74457803143892, (6, 2124): 198.045907729614, (6, 2134): 197.60044172513616, (6, 2138): 198.32134604290516, (6, 2141): 197.5776454306641, (6, 2148): 199.62345131727614, (6, 2150): 196.92173725735293, (6, 2151): 197.35615731381867, (6, 2152): 196.86468004697778, (6, 2153): 199.57158439879274, (6, 2154): 198.22453858278442, (6, 2155): 198.353770396672, (6, 2156): 197.92691755297759, (6, 2157): 199.23911413350035, (6, 2160): 199.5138284525142, (6, 2161): 196.9721590456698, (6, 2162): 200.2347598989258, (6, 2163): 199.75803260007544, (6, 2164): 199.82781876382666, (6, 2168): 197.86763275890084, (6, 2172): 198.8872673625093, (6, 2174): 197.52168859329117, (6, 2178): 199.35108089688356, (6, 2179): 199.21770881867394, (6, 2183): 198.48590248586603, (6, 2185): 198.6038660554879, (6, 2186): 198.3108438680917, (6, 2190): 199.39768858687958, (6, 2192): 198.9042755090635, (6, 2193): 198.51506351620299, (6, 2194): 198.01170848542142, (6, 2195): 198.1513267038605, (6, 2197): 199.11624716851787, (6, 2205): 198.71295224310688, (6, 2207): 198.12242752798724, (6, 2208): 198.49504319092492, (6, 2212): 198.19743263962675, (6, 2214): 191.92569980714276, (6, 2225): 193.6798047250371, (6, 2231): 186.84790986453558, (6, 2278): 199.83634467250042, (6, 2284): 201.17735601597929, (6, 2285): 201.18153787481518, (6, 2291): 200.1692689212236, (6, 2292): 199.2356164753666, (6, 2307): 200.56164702215293, (6, 2313): 200.2962398398296, (6, 2317): 198.04063846897287, (6, 2319): 199.6895862814287, (6, 2321): 200.3343609943528, (6, 2323): 199.95210580583628, (6, 2326): 201.09365755132566, (6, 2327): 200.6612531649334, (6, 2329): 200.39928584000296, (6, 2330): 200.17669254052274, (6, 2332): 201.03935567556732, (6, 2344): 199.4754177263493, (6, 2346): 199.67944935764712, (6, 2361): 197.6434978093874, (6, 2368): 203.76846399533278, (6, 2374): 204.418199017409, (6, 2375): 204.46734212447774, (6, 2377): 202.62877524759276, (6, 2378): 204.86486141927023, (6, 2379): 205.1306784846138, (6, 2380): 205.1383181522267, (6, 2383): 202.94097214779512, (6, 2385): 203.12270135930393, (6, 2395): 202.95364635506175, (6, 2397): 205.03138550867854, (6, 2398): 202.0679107881373, (6, 2399): 202.57310966908494, (6, 2400): 202.43194448335956, (6, 2402): 204.02336810887894, (6, 2403): 204.41792160473824, (6, 2404): 204.42809834857812, (6, 2405): 203.55957339437157, (6, 2407): 204.13450620095136, (6, 2408): 204.69231743917737, (6, 2409): 203.7880697734717, (6, 2411): 204.78647129883086, (6, 2412): 204.5436572986156, (6, 2413): 204.91819788795345, (6, 2414): 204.44278817739504, (6, 2422): 204.79612135386617, (6, 2424): 204.57347588614607, (6, 2426): 204.58332709312918, (6, 2433): 203.9968554781374, (6, 2436): 204.04596926422983, (6, 2437): 201.6914651252326, (6, 2440): 202.14373435926083, (6, 2445): 214.24293790224738, (6, 2447): 212.79279589854522, (6, 2454): 213.95350555966294, (6, 2455): 213.84128416308192, (6, 2460): 210.47426468325182, (6, 2461): 210.92833619133916, (6, 2471): 219.07843756025412, (6, 2492): 218.47517076082437, (6, 2511): 213.787590242662, (6, 2523): 216.21062116585185, (6, 2525): 216.0619081751991, (6, 2535): 213.27638578196655, (6, 2537): 212.61447752812998, (6, 2538): 212.89381602519566, (6, 2539): 213.54472074594662, (6, 2540): 213.5991264896847, (6, 2542): 214.3844911697045, (6, 2559): 223.330683779955, (6, 2575): 223.38585590327511, (6, 2599): 204.7010424418563, (6, 2600): 208.91503908604597, (6, 2607): 205.8083363353613, (6, 2627): 219.0562088126438, (6, 2647): 221.68302308571742, (6, 2674): 219.68745547535025, (6, 2681): 219.86819074701552, (6, 2683): 220.64930931148567, (6, 2686): 219.28855829082156, (6, 2689): 232.94759130260556, (6, 2690): 233.12258048962, (6, 2713): 238.99490579110486, (6, 2714): 239.66848743720382, (6, 2715): 239.9717303007542, (6, 2739): 239.5698826212225, (6, 2740): 236.39851830781862, (6, 2741): 236.46069027233938, (6, 2749): 239.62525686169366, (6, 2750): 239.56037849104388, (6, 2752): 239.70441259698282, (6, 2755): 240.04611896061598, (6, 2758): 240.11040883502415, (6, 2759): 240.03953131510423, (6, 2769): 239.50324549743328, (6, 2771): 237.21769562438726, (6, 2779): 238.47951256560734, (6, 2784): 235.53202055252413, (6, 2800): 237.30417664092374, (6, 2802): 236.42774276312525, (6, 2803): 236.16465468302047, (6, 2804): 235.90115138812814, (6, 2805): 237.1282087174787, (6, 2807): 236.96097970120144, (6, 2809): 237.17672180453556, (6, 2812): 234.82478692064558, (6, 2814): 238.0522467436353, (6, 2817): 239.44385058408167, (6, 2819): 236.63899410169032, (6, 2823): 236.29751564467696, (6, 2832): 237.72072574869753, (6, 2836): 236.310517312017, (6, 2839): 236.80644217304118, (6, 2841): 238.84173182757507, (6, 2843): 238.50075749890473, (6, 2846): 237.18584821790705, (6, 2849): 238.19015180745424, (6, 2852): 237.77532836434526, (6, 2853): 238.39019265497862, (6, 2876): 239.2210869816991, (6, 2877): 240.4535516703487, (6, 2885): 242.1953936571024, (6, 2918): 235.85305801599364, (6, 2921): 236.5186723487495, (6, 2925): 232.91646342950506, (6, 2926): 231.4391484176228, (6, 2930): 235.5341230955063, (6, 2931): 233.53617723519446, (6, 2938): 236.11643194675185, (6, 2940): 236.33217314521374, (6, 2947): 234.3298301580476, (6, 2949): 234.93715179579723, (6, 2950): 235.41105119226455, (6, 2952): 235.17577853186063, (6, 2958): 235.0241704976618, (6, 2959): 234.96505844599528, (6, 2960): 235.60415004797562, (6, 2961): 235.4603106413539, (6, 2963): 234.96532792434644, (6, 2968): 235.2703993276363, (6, 2976): 234.7469427384623, (6, 2981): 232.00225734752493, (6, 2982): 232.17610088070853, (6, 2984): 232.01146245778887, (6, 3003): 231.93640056527687, (6, 3046): 225.38741999405312, (6, 3050): 229.45141820198617, (6, 3051): 229.521316931423, (6, 3053): 229.13114833105504, (6, 3069): 232.5300200262114, (6, 3071): 228.31095057660886, (6, 3080): 242.7068996421516, (6, 3199): 233.0357086472085, (6, 3200): 232.70654134961867, (6, 3205): 235.83334778222894, (6, 3209): 233.02055566619242, (6, 3215): 232.57087136418187, (6, 3217): 231.95919863828027, (6, 3249): 232.44909403402417, (6, 3263): 237.00574272275014, (6, 3289): 233.43342331586155, (6, 3301): 234.01866642917798, (6, 3302): 233.6364422833777, (6, 3307): 233.3147682698114, (6, 3310): 234.28306131411654, (6, 3391): 243.24605358798877, (6, 3509): 130.06026297601252, (6, 3510): 129.67754030622578, (6, 3511): 129.66152753973864, (6, 3512): 129.18741628076484, (6, 3514): 129.05304671326888, (6, 3519): 132.28094382437087, (6, 3536): 130.2615013027708, (6, 3545): 130.59344361753776, (6, 3548): 129.64861717138868, (6, 3572): 130.80821953643363, (6, 3581): 131.2431653355631, (6, 3583): 129.86963618887881, (6, 3601): 133.42065662272046, (6, 3656): 133.82674772421825, (6, 3669): 135.30406668207763, (6, 3670): 135.74044510816537, (6, 3695): 132.86198559801187, (6, 3696): 133.09088402488368, (6, 3782): 125.0918099619116, (6, 3792): 125.38341080836138, (6, 3989): 165.60463489922603, (6, 4008): 168.38201875672547, (6, 4031): 169.1299696918093, (6, 4045): 167.259612007616, (6, 4144): 166.53445457454413, (6, 4145): 162.78403406825825, (6, 4164): 165.23520355619797, (6, 4168): 163.91958591144416, (6, 4173): 163.5181406798809, (6, 4181): 161.82797549318977, (6, 4228): 161.2505947179052, (6, 4248): 159.17760293142766, (6, 4254): 139.57324277077345, (6, 4260): 140.1218193387364, (6, 4262): 140.782466887737, (6, 4273): 140.8841572196382, (6, 4319): 128.92339761155046, (6, 4326): 128.73030192171242, (6, 4328): 128.99824045311652, (6, 4334): 129.17971493040875, (6, 4335): 128.85510633679576, (6, 4372): 72.97296159079129, (6, 4413): 78.87095441627625, (6, 4434): 73.00946308407065, (6, 4447): 74.85912944049977, (6, 4452): 72.95007482311074, (6, 4463): 53.00902715339034, (6, 4465): 53.86925257715476, (6, 4619): 77.16678757212681, (6, 4645): 79.41674503485176, (6, 4657): 78.81328782264823, (6, 4666): 77.81213733430606, (6, 4676): 79.13111108580853, (6, 4678): 79.56887161598192, (6, 4689): 78.31102600840426, (6, 4704): 84.82774629419423, (6, 4726): 95.52470774761713, (6, 4727): 95.286614535469, (6, 4730): 94.84133945671856, (6, 4731): 94.86948101015999, (6, 4734): 95.70539592696859, (6, 4735): 95.39418427324722, (6, 4736): 95.43008815978871, (6, 4737): 94.93020563869811, (6, 4738): 94.92158038775867, (6, 4756): 95.11152154280856, (6, 4760): 94.37405221075623, (6, 4761): 94.68758514771025, (6, 4762): 93.9467924285981, (6, 4765): 94.43420583922789, (6, 4773): 96.07656231093819, (6, 4774): 95.72036153650066, (6, 4790): 95.9395536772268, (6, 4795): 95.76782010903457, (6, 4799): 95.74878977087357, (6, 4801): 96.0626949674715, (6, 4804): 96.03129605539333, (6, 4805): 95.88958380727112, (6, 4806): 95.42069483190245, (6, 4815): 95.0669203020821, (6, 4816): 95.73397751885176, (6, 4817): 95.69563405672505, (6, 4826): 95.38307934870201, (6, 4830): 94.97204340361404, (6, 4839): 95.04271148278359, (6, 4840): 95.17604662977735, (6, 4841): 94.62225910359332, (6, 4846): 94.49039232384362, (6, 4848): 94.28532337117339, (6, 4850): 94.47229907223766, (6, 4871): 92.53654645401026, (6, 4883): 94.34147136817795, (6, 4900): 93.63595742274985, (6, 4901): 93.22310184391822, (6, 4917): 73.16355039608042, (6, 4931): 71.38680236404623, (6, 4944): 73.50434907107561, (6, 4956): 71.569979968899, (6, 4958): 71.24231739459599, (6, 4959): 70.71591358457594, (6, 4961): 72.04294177807304, (6, 4966): 70.97509726859636, (6, 5207): 68.9922511328061, (6, 5272): 61.6970775159717, (6, 5283): 61.64163213428376, (6, 5287): 60.214333051703505, (6, 5289): 60.15569923579719, (6, 5293): 63.051308132309906, (6, 5295): 63.108689541816936, (6, 5296): 62.27137268279055, (6, 5298): 61.80438511389088, (6, 5303): 61.135221193923364, (6, 5305): 60.0436658691088, (6, 5306): 58.834186542070896, (6, 5307): 59.969413663584334, (6, 5308): 59.77168015347796, (6, 5313): 60.84107369804621, (6, 5314): 61.16761786074896, (6, 5317): 59.21956378491213, (6, 5319): 60.88437671422843, (6, 5324): 61.49965710388585, (6, 5326): 61.949805860941304, (6, 5348): 58.10061448031112, (6, 5351): 56.92348542980585, (6, 5399): 58.98343231476786, (6, 5413): 55.11693516712096, (6, 5422): 59.83904734575118, (6, 5445): 59.32785931588003, (6, 5448): 59.27089007457219, (6, 5456): 58.3699292073543, (6, 5467): 58.19038743132071, (6, 5624): 61.12075677473879, (6, 5671): 74.46402851298352, (6, 5672): 74.3287090290382, (6, 5797): 77.88528889079524, (6, 5871): 54.445896605820074, (6, 5976): 51.34959149489348, (6, 6118): 198.70867803395285, (6, 6248): 214.15624926683375, (6, 6345): 107.0150669762249, (6, 6352): 107.56911109986676, (6, 6354): 106.61140343502942, (6, 6359): 107.0009574807834, (6, 6376): 108.68334019607993, (6, 6378): 106.72920542928522, (6, 6381): 107.3842556008648, (6, 6383): 106.93152178883376, (6, 6396): 109.38855723245231, (6, 6399): 107.60166959439898, (6, 6408): 107.05407097824332, (6, 6409): 105.48623020429466, (6, 6419): 104.370446774729, (6, 6422): 105.95196156743754, (6, 6423): 105.92465154101855, (6, 6424): 105.20000649672389, (6, 6439): 104.87806394065413, (6, 6464): 104.61451253523447, (6, 6465): 105.11522642630378, (6, 6469): 105.99564069402518, (6, 6470): 106.24664507047183, (6, 6472): 107.02377838236667, (6, 6480): 104.966825786073, (6, 6486): 102.40361941723553, (6, 6497): 103.1498103769154, (6, 6503): 101.95213937131241, (6, 6508): 103.33905603741864, (6, 6509): 102.59617426986762, (6, 6521): 103.93725873934063, (6, 6544): 102.61150005000286, (6, 6552): 103.53211250588726, (6, 6553): 103.47121904190433, (6, 6554): 103.42871739384525, (6, 6578): 103.83495106213067, (6, 6582): 102.39485487941582, (6, 6601): 103.55959543297543, (6, 6609): 105.26709958210105, (6, 6610): 104.97614032454982, (6, 6611): 105.75245862422581, (6, 6614): 106.20069037493403, (6, 6615): 105.93622181990118, (6, 6616): 104.95811279531851, (6, 6617): 105.30056306868273, (6, 6618): 104.3191661697829, (6, 6619): 106.03063615783026, (6, 6620): 104.47861965460842, (6, 6621): 104.3619099768303, (6, 6622): 104.6988687550716, (6, 6623): 105.67648726933358, (6, 6624): 105.15968001060793, (6, 6625): 105.41529831709008, (6, 6626): 106.23883526141948, (6, 6627): 106.61466420007103, (6, 6628): 103.98513093084028, (6, 6629): 104.57464066956315, (6, 6630): 106.17019740090278, (6, 6632): 104.83968284685858, (6, 6634): 105.84788969666748, (6, 6635): 104.61518661981498, (6, 6636): 104.79295703654735, (6, 6637): 104.49916831596387, (6, 6638): 105.7160507951637, (6, 6639): 106.33726546824889, (6, 6640): 105.96089513855918, (6, 6641): 103.98494118757102, (6, 6642): 105.39710792287197, (6, 6643): 106.57782307871278, (6, 6645): 105.81515588458309, (6, 6646): 104.69020943271171, (6, 6647): 105.57904558613171, (6, 6653): 106.08291119276768, (6, 6655): 106.49282058088991, (6, 6658): 105.65949528197028, (6, 6662): 105.05305393409508, (6, 6819): 99.08718105851322, (6, 6996): 91.34051270958386, (6, 7059): 91.5812746001599, (6, 7187): 74.92491786431638, (6, 7304): 84.98946766158058, (6, 7528): 84.27539655420006, (6, 7720): 93.90251722071228, (6, 7793): 91.21115929322347, (6, 7807): 92.13827941887394, (6, 7808): 90.5870111278195, (6, 7831): 102.14625998351694, (6, 7850): 105.10170473780138, (6, 7852): 105.62030893544784, (6, 8012): 97.1725431208412, (6, 8125): 80.78459954192137, (6, 8208): 95.86660752072807, (6, 8392): 95.12813733658125, (6, 8651): 101.39426943464213, (6, 9088): 108.57301522758509, (6, 9443): 80.29899198439276, (6, 9444): 79.71489034018838, (6, 9828): 79.77745820339435, (6, 9868): 88.7548292230864, (6, 10180): 79.7879819948816, (6, 10256): 83.06311991045814, (6, 10276): 83.36275253971802, (6, 10378): 90.347314969183, (6, 10676): 68.58957453079461, (6, 10714): 63.81537451965264, (6, 10730): 71.83688740930866, (6, 10862): 12.5, (6, 10881): 12.5, (6, 10883): 12.5, (6, 10885): 12.5, (6, 10891): 12.5, (6, 10909): 12.5, (6, 10911): 12.5, (6, 10913): 12.5, (6, 10915): 12.5, (6, 10919): 12.5, (6, 11037): 12.5, (6, 11039): 12.5, (6, 11516): 203.41688207777872, (6, 11856): 129.37670210970006, (6, 11857): 128.27882480586996, (6, 11861): 128.82221513599254, (6, 11881): 129.47312645775258, (6, 11902): 128.04893894784786, (6, 11911): 128.5681340315293, (6, 11914): 128.42597349572554, (6, 11922): 129.21306385433195, (6, 11924): 129.74760257709337, (6, 11926): 129.3826021037567, (6, 11950): 131.03951753528452, (6, 11963): 132.26559336159937, (6, 11983): 132.73833219350374, (6, 11985): 132.8156393523622, (6, 12009): 133.71661065673942, (6, 12010): 132.55609196175726, (6, 12018): 132.8569894040169, (6, 12020): 132.92915601612108, (6, 12021): 133.20232802035048, (6, 12024): 134.0498353694322, (6, 12025): 133.52763013027064, (6, 12027): 133.38495738528655, (6, 12031): 132.40202782234323, (6, 12032): 132.51228699107642, (6, 12035): 133.92597367022503, (6, 12041): 132.24844813334698, (6, 12045): 122.01163365530549, (6, 12145): 128.41040970079396, (6, 12275): 168.73289850657574, (6, 12294): 167.5929835134781, (6, 12358): 176.24449039919662, (6, 12463): 180.4359244224558, (6, 12465): 180.42162257973524, (6, 12482): 180.61267788674323, (6, 12503): 180.70748975914663, (6, 12506): 181.02883214964325, (6, 12549): 179.03908316190274, (6, 12559): 179.05316112607656, (6, 12569): 179.77534656106852, (6, 12572): 179.99013780914188, (6, 12574): 179.3985725055423, (6, 12576): 179.161379970645, (6, 12591): 178.35832650389452, (6, 12608): 179.74536460401043, (6, 12696): 176.1616439655639, (6, 12710): 176.97437885405714, (6, 12728): 177.15554858968773, (6, 12766): 128.46589747213628, (6, 12771): 123.16322391242203, (6, 12790): 123.02111061193057, (6, 12795): 123.1214291902441, (6, 12797): 118.45915728806807, (6, 12798): 118.6819554915542, (6, 12811): 120.99422899573, (6, 12830): 120.85381137766878, (6, 12848): 119.96028802498222, (6, 12850): 119.37622645631754, (6, 12852): 120.35700703892111, (6, 12854): 120.01499531248335, (6, 12859): 119.96515810639814, (6, 12861): 118.76550565897985, (6, 12865): 121.98846576327762, (6, 12866): 121.42993983024134, (6, 12867): 122.4687465031728, (6, 12874): 122.01741451417611, (6, 12875): 122.11873719122768, (6, 12881): 121.47906778821927, (6, 12883): 121.86136575321702, (6, 12885): 122.43448823654865, (6, 12888): 121.41281769298732, (6, 12889): 121.0680822840355, (6, 12892): 122.237847520396, (6, 12893): 121.689729819523, (6, 12896): 121.62986831388302, (6, 12906): 123.19855010820143, (6, 13018): 127.18095213017861, (6, 13071): 128.75635982225847, (6, 13131): 120.22708839186735, (6, 13146): 120.87096559364353, (6, 13159): 126.35178758912477, (6, 13193): 119.40064931551078, (6, 13198): 113.58400555052151, (6, 13292): 116.48975681269857, (6, 13296): 114.80535603281726, (6, 13406): 116.32222694652599, (6, 13407): 116.59787330510899, (6, 13417): 119.28401703072252, (6, 13418): 120.03439481899365, (6, 13438): 118.9530993078097, (6, 13442): 118.23811520167189, (6, 13443): 118.13008811579677, (6, 13764): 130.7446065268093, (6, 13766): 130.68171917461697, (6, 13771): 131.86716397293876, (6, 13783): 128.91773057647902, (6, 13784): 130.13072142663654, (6, 13792): 133.684237459367, (6, 13824): 129.1899221045381, (6, 14017): 122.25931068876667, (6, 14870): 16.36398851179398, (6, 14997): 73.62749907714434, (6, 15000): 72.99802117192081, (6, 15003): 72.3674565921425, (6, 15006): 75.15117049761906, (6, 15007): 75.09125062083784, (6, 15056): 73.20296086965303, (6, 15063): 72.82644113689457, (6, 15069): 72.1083672920506, (6, 15076): 74.6457878332425, (6, 15086): 75.44573902283103, (6, 15087): 74.56466511500147, (6, 15111): 75.22501080602062, (6, 15116): 74.77772612649963, (6, 15722): 76.50195196451416, (6, 15998): 62.24179585637725, (6, 16073): 183.36420154511325, (6, 16939): 185.27173726167928, (6, 16940): 184.567011750537, (6, 16951): 186.00992897542113, (6, 16963): 185.9192870552515, (6, 16965): 186.49513211592068, (6, 16969): 186.68938603527076, (6, 16970): 186.00316395381824, (6, 16971): 185.46123836490165, (6, 16973): 185.655972605921, (6, 16974): 186.9477588012001, (6, 16976): 185.89920202456048, (6, 16978): 185.4221567909526, (6, 16980): 185.90362013934148, (6, 16982): 187.18407324267085, (6, 17045): 223.80889846930904, (6, 17048): 224.66060192895256, (6, 17304): 154.00941548912496, (6, 17305): 154.2897339438614, (6, 17330): 154.45990005656523, (6, 17334): 153.09797247392936, (6, 17343): 155.18863814050718, (6, 17345): 153.78815035069834, (6, 17347): 154.87217969050317, (6, 17351): 152.02855588894244, (6, 17372): 153.28236576897015, (6, 17373): 155.0330651438474, (6, 17377): 155.2146078614446, (6, 17382): 154.22616604525618, (6, 17383): 154.16953312520545, (6, 17389): 153.64452380859757, (6, 17400): 154.53297694597615, (6, 17401): 154.39958438540575, (6, 17402): 154.6605568048819, (6, 17403): 154.8172006825431, (6, 17440): 154.62505170823846, (6, 17455): 155.48728694207452, (6, 17491): 156.10876264834562, (6, 17507): 150.83775128346733, (6, 17509): 151.17690225330148, (6, 17590): 152.48400542147243, (6, 17615): 144.92783553318688, (6, 17642): 145.81774645765466, (6, 17643): 146.05366417621562, (6, 17668): 144.72984150269716, (6, 17721): 141.9073028641083, (6, 17754): 146.37159057749113, (6, 17769): 150.18583968787968, (6, 17776): 149.44245278017652, (6, 17804): 150.90198838702088, (6, 17809): 151.4216823043653, (6, 17824): 150.62546295045965, (6, 17837): 151.26276156633276, (6, 17838): 151.72597450468592, (6, 17862): 151.53713998319023, (6, 17866): 152.44132714557625, (6, 17872): 150.92055312539378, (6, 17873): 150.324645196022, (6, 17881): 151.3005250672725, (6, 17947): 123.75849363635639, (6, 17951): 123.11642783067329, (6, 17953): 122.73759406950063, (6, 17954): 122.61422166284441, (6, 17959): 124.06590617438826, (6, 17963): 124.28626100228568, (6, 18000): 120.38895467920491, (6, 18001): 120.16321166110305, (6, 18111): 120.54841807499928, (6, 18148): 97.79981542464533, (6, 18166): 104.7280817830692, (6, 18189): 114.62120430844907, (6, 18239): 155.0261576155488, (6, 18240): 155.09756292696966, (6, 18245): 155.11493628488628, (6, 18247): 155.08377055342217, (6, 18251): 155.2073984169792, (6, 18256): 155.431757797794, (6, 18258): 155.34599005061642, (6, 18259): 155.41125598906396, (6, 18260): 155.5203152587369, (6, 18262): 155.67056201638198, (6, 18263): 155.510151721755, (6, 18264): 155.6136729681671, (6, 18266): 155.77821831193, (6, 18267): 155.8685520998575, (6, 18268): 155.94187749368277, (6, 18269): 156.1301110087583, (6, 18275): 156.0416581645555, (6, 18285): 155.5479031530042, (6, 18308): 153.56920438058188, (6, 18313): 153.11741362025256, (6, 18314): 153.56664987939158, (6, 18315): 155.90649613496785, (6, 18316): 155.99712415031632, (6, 18317): 156.09170486632334, (6, 18320): 156.0306873172762, (6, 18321): 156.12945368866008, (6, 18322): 156.25740674086634, (6, 18324): 156.2139337681487, (6, 18325): 156.46811348555931, (6, 18326): 156.36864320674792, (6, 18327): 156.26489251872846, (6, 18329): 156.46670424186468, (6, 18330): 156.66150616971078, (6, 18331): 156.44057404749978, (6, 18332): 156.26644606082743, (6, 18333): 156.54302015802233, (6, 18336): 156.24557639488916, (6, 18337): 156.26583130647543, (6, 18403): 156.7185159509361, (6, 18432): 156.26343120147007, (6, 18451): 156.58956173424173, (6, 18466): 156.61440379231232, (6, 18481): 155.6975342763494, (6, 18483): 155.77098107106582, (6, 18484): 155.57468234832572, (6, 18485): 154.9084021008633, (6, 18486): 155.0194722219962, (6, 18487): 154.60362053003257, (6, 18489): 155.23176293814612, (6, 18490): 155.35565515754533, (6, 18491): 155.50884995109354, (6, 18492): 154.33874773855365, (6, 18493): 154.87624890826046, (6, 18494): 155.22952940698642, (6, 18495): 155.23037485605832, (6, 18496): 155.13079136185914, (6, 18497): 154.4388566902914, (6, 18498): 154.8168485179251, (6, 18499): 155.08332574341168, (6, 18501): 154.75892688807312, (6, 18502): 154.57980449148604, (6, 18503): 154.53317624126478, (6, 18504): 155.28578997178775, (6, 18506): 154.5699850957506, (6, 18507): 154.35654457876757, (6, 18508): 154.9740248263391, (6, 18509): 154.90678483430327, (6, 18510): 154.4332617602561, (6, 18511): 154.77539077094175, (6, 18512): 154.71637965349072, (6, 18515): 155.19629512495482, (6, 18516): 154.96473948796339, (6, 18517): 154.63146504900874, (6, 18518): 155.17027547328152, (6, 18519): 155.3652632969416, (6, 18520): 155.01280604013132, (6, 18522): 156.22390156136075, (6, 18523): 156.1779259800014, (6, 18532): 156.2888638094065, (6, 18535): 155.9752604098683, (6, 18537): 155.80077180013635, (6, 18539): 155.794877093721, (6, 18540): 155.77036642551224, (6, 18541): 155.81921080061716, (6, 18542): 155.8579667172551, (6, 18543): 155.63233552580598, (6, 18546): 155.60146070192926, (6, 18555): 155.86756584932053, (6, 18556): 155.86058537503925, (6, 18565): 156.15920488690693, (6, 18567): 156.077454857853, (6, 18568): 156.00044253110303, (6, 18577): 157.07974346021103, (6, 18583): 157.12192651132509, (6, 18605): 157.61737493422973, (6, 18608): 155.84372479038845, (6, 18616): 158.61217760917268, (6, 18618): 159.31934072185476, (6, 18625): 159.6205741168058, (6, 18645): 159.10789511340926, (6, 18646): 159.11007175530187, (6, 18653): 157.8306312534099, (6, 18654): 158.49342851855224, (6, 18655): 157.93559043804837, (6, 18666): 161.71474038338368, (6, 18837): 167.14427990423846, (6, 18974): 158.43876780611188, (6, 18999): 160.1494181567378, (6, 19000): 160.4305455493144, (6, 19174): 152.99055248184624, (6, 19342): 160.1395982784799, (6, 19455): 150.87153034984343, (6, 19555): 141.17234404930068, (6, 19564): 144.61102360632853, (6, 19573): 143.49849031548777, (6, 19586): 142.82607982090062, (6, 19605): 142.59396736774846, (6, 19611): 143.24356748140423, (6, 19614): 142.21153502845158, (6, 19641): 149.86010840398288, (6, 19702): 150.55205438036867, (6, 19713): 149.81747659809488, (6, 19731): 135.10453710047636, (6, 19819): 150.4843097833667, (6, 19893): 96.55877755759182, (6, 19899): 97.11757320433634, (6, 19929): 97.31467987084035, (6, 19951): 100.81965383271302, (6, 19962): 96.39152860247216, (6, 19970): 99.54184928345238, (6, 19971): 99.00047734175389, (6, 19972): 98.30655058476077, (6, 19975): 98.56386082001153, (6, 19978): 104.04916329232677, (6, 19987): 104.4772354002399, (6, 19989): 103.42451395848074, (6, 20039): 104.8506747749455, (6, 20043): 105.80228019520464, (6, 20047): 105.89814787652273, (6, 20052): 104.32368209156913, (6, 20054): 104.1742446118869, (6, 20085): 113.09760926622899, (6, 20104): 113.58060869213105, (6, 20132): 110.16508832842779, (6, 20203): 91.20262864889574, (6, 20280): 89.1368500530357, (6, 20285): 88.34034578516622, (6, 20290): 89.64196985133835, (6, 20297): 89.40933774182055, (6, 20309): 100.59628674656351, (6, 20453): 110.67832732573504, (6, 20485): 87.91738414455311, (6, 20520): 87.5324353759749, (6, 20526): 85.44030507120691, (6, 20698): 152.08299582626182, (6, 20868): 161.0568498511507, (6, 21042): 104.05540932648977, (6, 21057): 107.6153022278043, (6, 21066): 105.03346238220622, (6, 21075): 105.55593681952682, (6, 21093): 103.16523167748018, (6, 21098): 104.01892131604744, (6, 21127): 103.72929640355758, (6, 21130): 103.82723488238251, (6, 21144): 104.81298161748741, (6, 21146): 103.50732618548875, (6, 21147): 105.0800234466317, (6, 21148): 105.30485671250601, (6, 21153): 108.12599200162546, (6, 21293): 108.48380228411195, (6, 21426): 117.81831750624373, (6, 21442): 123.41145682035581, (6, 21451): 123.90727582619037, (6, 21466): 120.05747448967497, (6, 21469): 120.39343821137297, (6, 21471): 119.91031980344123, (6, 21473): 120.0637163060486, (6, 21475): 119.79052648907755, (6, 21482): 121.01402377071857, (6, 21484): 120.72910953863679, (6, 21488): 120.64204205548054, (6, 21494): 119.22050888410364, (6, 21498): 119.6153136805842, (6, 21500): 118.54232176619418, (6, 21514): 117.37600248235317, (6, 21537): 117.17735858625575, (6, 21662): 116.31976689724215, (6, 21691): 114.47028258157465, (6, 21757): 115.64780986412882, (6, 21777): 94.01728250531288, (6, 21778): 93.61829941664735, (6, 21779): 93.27475986866078, (6, 21790): 95.08160977529197, (6, 21802): 93.95677170658479, (6, 21824): 93.82378643696657, (6, 21874): 92.68454237832987, (6, 21879): 91.40837902667512, (6, 21983): 98.81259701733691, (6, 22002): 99.74936066237488, (6, 22132): 109.5537711153774, (6, 22261): 66.8047845922227, (6, 22298): 64.71481669481693, (6, 22339): 66.39328798404628, (6, 22508): 60.92580254425834, (6, 22841): 258.7946702356481, (6, 22842): 258.646633737932, (6, 22874): 256.4872755702529, (6, 22941): 257.1714764739844, (6, 22956): 258.0420902193122, (6, 22960): 258.70081963527207, (6, 22968): 257.6109182435469, (6, 22970): 258.18631773449926, (6, 22974): 257.3645070616307, (6, 22980): 258.55387462317947, (6, 23025): 256.5276973719879, (6, 23028): 255.86621711562205, (6, 23081): 255.4859716966086, (6, 23104): 250.0243082429266, (6, 23147): 245.05418959680023, (6, 23298): 123.19436210346028, (6, 23376): 121.48669313971746, (6, 23381): 118.10592513376692, (6, 23529): 122.38157130415482, (6, 23556): 121.68090967969742, (6, 23718): 124.10233544207742, (6, 24001): 134.04329588534208, (6, 24094): 133.61516849085356, (6, 24129): 135.4270960447764, (6, 24174): 130.18764656555578, (6, 24235): 133.2407554965486, (6, 24259): 135.94698226803897, (6, 24260): 135.6699055498593, (6, 24261): 135.41638636547975, (6, 24305): 138.43602121126827, (6, 24306): 138.597702188308, (6, 24307): 138.17538600015837, (6, 24308): 140.95234195683864, (6, 24498): 145.9153693323344, (6, 24499): 145.8880283283405, (6, 24500): 145.6215355545286, (6, 24668): 146.9549832342213, (6, 24711): 146.67862927865966, (6, 24756): 146.6931011189008, (6, 24788): 147.73132967150258, (6, 24809): 144.46967408995908, (6, 24813): 145.5895242871201, (6, 24821): 145.26796895828394, (6, 24825): 145.306488721563, (6, 24832): 144.40841996638315, (6, 24833): 144.79107048605226, (6, 24835): 145.1118612325041, (6, 24837): 145.86268029075163, (6, 24840): 144.2762059757541, (6, 24841): 145.01847889231541, (6, 24844): 144.19481409530974, (6, 24845): 144.9291482793184, (6, 24846): 144.35322985909258, (6, 24849): 144.51463164379967, (6, 24850): 145.58614250488733, (6, 24863): 140.99359472917854, (6, 24866): 141.71099312121703, (6, 24885): 142.18693886412134, (6, 24886): 142.03053776732406, (6, 24889): 144.30053710154735, (6, 24903): 145.21792906943645, (6, 24909): 143.24837828603756, (6, 24999): 175.34804953252745, (6, 25019): 175.29067129713718, (6, 25028): 174.77184805897195, (6, 25137): 83.53198430368185, (6, 25145): 84.29178543858298, (6, 25208): 87.94783125410389, (6, 25233): 86.72410663304017, (6, 25371): 87.34741280207969, (6, 25377): 86.47896826274966, (6, 25828): 60.56779052363776, (6, 25851): 61.62874036666409, (6, 25874): 62.74321631492176, (6, 25898): 60.66241287021539, (6, 25946): 60.501677931726896, (6, 26047): 61.26983035615473, (6, 26066): 84.54128298840978, (6, 26197): 71.74908682142001, (6, 26212): 43.37919829964598, (6, 26253): 42.05756978483816, (6, 26254): 42.82453148403048, (6, 26257): 42.407793721321845, (6, 26258): 42.059065384301995, (6, 26260): 42.30042809548895, (6, 26266): 43.824196787065006, (6, 26267): 43.791197041205166, (6, 26271): 43.55184842223871, (6, 26304): 49.552133698060075, (6, 26305): 50.137005921607816, (6, 26363): 55.7174529145733, (6, 26441): 48.95920920974461, (6, 26442): 49.104265204952114, (6, 26450): 48.31279869557481, (6, 26459): 47.00249271044429, (6, 26462): 46.561978384266006, (6, 26467): 48.76264356668046, (6, 26471): 48.74653953637556, (6, 26472): 48.86168208642846, (6, 26473): 49.01147628308244, (6, 26476): 50.482867543323046, (6, 26485): 47.9806933749845, (6, 26493): 48.644864336035646, (6, 26524): 46.33054599253268, (6, 26525): 46.58403336212689, (6, 26556): 48.388093042773654, (6, 26560): 47.29370816678668, (6, 26561): 46.579194135606286, (6, 26564): 48.46582637848684, (6, 26569): 46.80239744112202, (6, 26570): 47.00861975501716, (6, 26573): 47.67853909889755, (6, 26581): 48.153368697582515, (6, 26583): 47.688509403908085, (6, 26593): 48.78276156725901, (6, 26837): 49.4059501942411, (6, 26844): 49.70678497746942, (6, 26863): 50.25539699530562, (6, 26893): 51.57120716067008, (6, 26902): 52.032827493410224, (6, 26905): 50.52101944576528, (6, 26912): 51.21578108023746, (6, 26921): 50.80381308075832, (6, 26922): 51.69669831729756, (6, 27212): 32.93034177183727, (6, 27218): 31.49138943107974, (6, 27239): 34.38694678238425, (6, 27257): 33.910301509878984, (6, 27274): 34.776774070403015, (6, 27279): 34.862819155864514, (6, 27282): 34.07195308039849, (6, 27283): 33.92750694833993, (6, 27285): 35.27706912891643, (6, 27286): 34.96345553686968, (6, 27290): 33.44117924149271, (6, 27295): 32.5948219215849, (6, 27300): 34.82423604943526, (6, 27344): 33.82637870447694, (6, 27366): 34.94445897357755, (6, 27383): 35.8387198723211, (6, 27398): 36.24962862404216, (6, 27406): 35.28348637546672, (6, 27407): 35.3433745232323, (6, 27426): 32.84433476257884, (6, 27432): 29.75192211150386, (6, 27460): 31.47457679333427, (6, 27523): 39.57344766502879, (6, 27545): 49.24988614946892, (6, 27602): 70.17074598176602, (6, 27606): 70.34866869271713, (6, 27646): 53.84496928120941, (6, 27667): 57.67586070423559, (6, 27672): 57.699925216597265, (6, 27674): 57.152554324369305, (6, 27688): 57.00928972711748, (6, 27692): 58.572687030278225, (6, 27693): 58.03136049489083, (6, 27705): 58.20582116634946, (6, 27712): 58.64454915041028, (6, 27786): 67.29543572066113, (6, 27790): 64.13330308819627, (6, 27791): 63.84038619024772, (6, 27795): 66.20792925798972, (6, 27801): 63.87867741697652, (6, 27813): 68.04736618096183, (6, 27816): 67.09850112884749, (6, 27823): 63.78546216309597, (6, 27830): 65.97138985346525, (6, 27884): 50.06537524472083, (6, 27885): 52.597203010110384, (6, 27896): 50.879963428825526, (6, 27919): 50.54159860039531, (6, 27922): 51.1923951205303, (6, 27930): 50.11460452104068, (6, 27934): 50.41574731298793, (6, 27935): 50.72334578582583, (6, 27948): 75.9771708355598, (6, 27951): 74.1445331006702, (6, 28061): 90.9363528658598, (6, 28290): 116.69028429352342, (6, 28292): 118.31868060027004, (6, 28293): 117.08125148317907, (6, 28295): 117.37978360735055, (6, 28296): 116.96972846595345, (6, 28297): 115.89084349240773, (6, 28302): 116.1741942148972, (6, 28310): 176.65050924470123, (6, 28313): 178.45123519496724, (6, 28372): 176.1665701062237, (6, 28398): 176.4033093981265, (6, 28399): 176.3204173366124, (6, 28400): 176.76695522819614, (6, 28401): 175.29446975921138, (6, 28445): 178.81859441199722, (6, 28475): 172.71393623609623, (6, 28885): 127.25763812569473, (6, 28886): 126.67167029270315, (6, 28915): 125.93852622910183, (6, 28916): 125.98339976183833, (6, 28917): 125.581977954681, (6, 28921): 128.09846807444703, (6, 28931): 127.73790357535434, (6, 28945): 122.64592713528754, (6, 28982): 124.19108815194551, (6, 29219): 120.59517225612758, (6, 29228): 119.37183274103623, (6, 29246): 124.92250381060315, (6, 29248): 123.82266972352559, (6, 29282): 122.3927135071523, (6, 29290): 126.7497250493036, (6, 29291): 126.14488203999328, (6, 29292): 126.57069669800241, (6, 29293): 125.95992513494483, (6, 29294): 126.0300303825279, (6, 29298): 125.74655686185346, (6, 29299): 125.4308815996819, (6, 29304): 125.44520917579621, (6, 29317): 124.34997940554163, (6, 29323): 124.29617840538532, (6, 29330): 124.7733547541486, (6, 29331): 125.23457263571137, (6, 29344): 118.66707122027834, (6, 29445): 100.49343091729416, (6, 29724): 261.75757780396634, (6, 29738): 262.06342629601716, (6, 29745): 261.3841195840501, (6, 29748): 262.6378091529368, (6, 29750): 263.59090725663526, (6, 29759): 262.0861820053781, (6, 29772): 263.23490588870624, (6, 29781): 263.0149604216902, (6, 29784): 262.3563472472741, (6, 29790): 263.45452601027904, (6, 29811): 263.27718057887466, (6, 29817): 268.1899931786817, (6, 29818): 267.99331477499555, (6, 29929): 260.6037551676719, (6, 30039): 261.58212304459164, (6, 30066): 257.24850833687265, (6, 30116): 249.20942068513656, (6, 30238): 237.2118315208102, (6, 30248): 239.97500843257805, (6, 30260): 239.83359826103205, (6, 30545): 126.07219993130559, (6, 30733): 115.31208862683903, (6, 30756): 106.0611319371553, (6, 30921): 114.34120339767586, (6, 31079): 121.63680797620353, (6, 31149): 115.02160569611245, (6, 31154): 115.93964085882946, (6, 31160): 114.82415020639161, (6, 31163): 115.76956939841398, (6, 31189): 109.56617769664577, (6, 31215): 110.76254841593718, (6, 31259): 114.29818107062027, (6, 31262): 113.4398199767561, (6, 31430): 124.7555867240096, (6, 31568): 119.61270405600598, (6, 31751): 121.02147733145567, (8, 109): 134.95103562987643, (8, 872): 297.15389085953717, (8, 873): 298.0323503015296, (8, 877): 297.6734061824279, (8, 879): 297.8008390035056, (8, 884): 296.8520667814053, (8, 889): 297.4166465841836, (8, 891): 296.56944023897324, (8, 892): 298.4878636457684, (8, 894): 298.3890445930426, (8, 896): 297.59125324149903, (8, 903): 297.6726123422774, (8, 909): 296.2731334031728, (8, 910): 296.6519202384418, (8, 912): 296.0643461256218, (8, 913): 295.40704927831405, (8, 916): 295.1680095163791, (8, 926): 296.97541656171103, (8, 927): 296.68623450223186, (8, 948): 296.25586441923645, (8, 961): 296.8810610931709, (8, 962): 296.9996382355532, (8, 963): 297.12680539890516, (8, 967): 298.05601046761217, (8, 974): 297.5151867022596, (8, 998): 298.37911070627746, (8, 1014): 317.936095215015, (8, 1086): 295.6992570117283, (8, 1087): 295.66190117708953, (8, 1089): 294.8074385514864, (8, 1090): 295.1742159485858, (8, 1092): 296.44878142098224, (8, 1097): 295.4619595943605, (8, 1107): 297.1300314561956, (8, 1387): 162.25371934777615, (8, 1554): 148.21298126053847, (8, 1827): 336.4186848564294, (8, 1828): 336.5310041750663, (8, 1829): 336.65205645792474, (8, 1830): 336.4217836859755, (8, 1831): 336.5166556504792, (8, 1832): 336.4313604481922, (8, 1833): 336.4576810025707, (8, 1836): 336.37450343584004, (8, 1841): 336.9120440476444, (8, 1843): 336.67715246381806, (8, 1844): 336.76608332327515, (8, 1845): 336.4726593249456, (8, 1847): 335.6134987099014, (8, 1848): 335.91960217987685, (8, 1849): 337.3383578786395, (8, 1850): 337.50316383969044, (8, 1851): 336.1119955285584, (8, 1852): 336.09810302941827, (8, 1854): 336.2734797160673, (8, 1856): 335.52204078656484, (8, 1857): 335.87892316104137, (8, 1858): 337.22416195997516, (8, 1861): 336.6015490888322, (8, 1866): 335.47105821848726, (8, 1867): 336.9588527145711, (8, 1868): 336.79981344284107, (8, 1870): 336.69323383655507, (8, 1871): 336.94667817815326, (8, 1875): 336.2824641802172, (8, 1880): 335.7467837432004, (8, 1882): 335.7858110850844, (8, 1883): 337.55648988166166, (8, 1889): 335.9681124548738, (8, 1893): 336.7276730753844, (8, 1894): 336.51822991425644, (8, 1899): 335.79904702991115, (8, 1900): 335.9731021628055, (8, 1902): 337.1087275232369, (8, 1905): 337.368486905337, (8, 1907): 336.16695390707736, (8, 1910): 336.31577784099494, (8, 1917): 338.08153315681164, (8, 1920): 336.21985761863294, (8, 1935): 337.4760799184267, (8, 1937): 337.70579963243273, (8, 1946): 335.3911620154096, (8, 1949): 335.68050936400647, (8, 1950): 334.6383204409953, (8, 1951): 335.12184574083, (8, 1952): 335.37466890949224, (8, 1953): 335.60906790913697, (8, 1954): 335.3302910070124, (8, 1958): 335.565402057242, (8, 1960): 336.00424409675975, (8, 1968): 336.1776026703877, (8, 1969): 337.6001526731322, (8, 1974): 337.2220763072141, (8, 1975): 337.19568252509083, (8, 1979): 336.58153188627205, (8, 1980): 336.4623552770805, (8, 1981): 336.6973805834188, (8, 1985): 336.87472226462336, (8, 1994): 334.1095074771082, (8, 2011): 335.750573291222, (8, 2019): 337.94714458554387, (8, 2020): 337.6562457187688, (8, 2029): 336.48369828521356, (8, 2030): 337.4556931785467, (8, 2032): 336.25679189397437, (8, 2033): 336.9140547365351, (8, 2034): 336.868895451692, (8, 2036): 335.5644232432157, (8, 2037): 335.90401158266224, (8, 2038): 336.1659021404551, (8, 2042): 339.6298618526079, (8, 2050): 336.8079029938143, (8, 2051): 336.7209729692874, (8, 2053): 336.82917203762, (8, 2054): 337.1344498946699, (8, 2066): 336.50669872499935, (8, 2067): 336.52757916392875, (8, 2071): 333.548484733314, (8, 2072): 334.15203480555493, (8, 2073): 332.65810559115164, (8, 2074): 332.55757719093197, (8, 2080): 331.52542686309073, (8, 2082): 334.4695146194698, (8, 2083): 334.7837643650147, (8, 2089): 334.1733745413001, (8, 2090): 334.47243255251254, (8, 2092): 334.110445955007, (8, 2098): 331.9438345326548, (8, 2099): 332.2608443073047, (8, 2101): 331.85278076681504, (8, 2102): 333.47384834024075, (8, 2103): 332.9518697356524, (8, 2104): 332.6521094173207, (8, 2106): 334.97257143462025, (8, 2112): 332.040192775018, (8, 2113): 333.68604335862386, (8, 2114): 334.0243919057511, (8, 2117): 335.18860484113446, (8, 2123): 333.9355325855159, (8, 2124): 334.26989140821945, (8, 2134): 333.25197439574697, (8, 2138): 334.2619510222355, (8, 2141): 333.38799301017696, (8, 2148): 333.6169607884775, (8, 2150): 332.5621222754888, (8, 2151): 332.89534184700864, (8, 2152): 332.35994073773054, (8, 2153): 333.75521842366226, (8, 2154): 332.3867631427399, (8, 2155): 332.18232408616933, (8, 2156): 331.95685966816075, (8, 2157): 332.14183179931035, (8, 2160): 334.606147689447, (8, 2161): 332.2769242416228, (8, 2162): 333.7117278643673, (8, 2163): 333.2512370138977, (8, 2164): 333.20333648812453, (8, 2168): 332.5653638818042, (8, 2172): 332.75662708175554, (8, 2174): 332.8227642132994, (8, 2178): 332.99489135882794, (8, 2179): 332.768496917537, (8, 2183): 334.2098229819081, (8, 2185): 334.2151815442626, (8, 2186): 333.95664240578526, (8, 2190): 334.69986394492656, (8, 2192): 334.22899623924866, (8, 2193): 334.31230985172954, (8, 2194): 333.8310891753452, (8, 2195): 333.72790903566965, (8, 2197): 334.3154730825048, (8, 2205): 333.59406552226346, (8, 2207): 332.6657918985732, (8, 2208): 333.17815186366687, (8, 2212): 334.52582115450787, (8, 2214): 324.1975977896555, (8, 2225): 325.25453060070316, (8, 2231): 323.6979700784287, (8, 2278): 329.81932943230134, (8, 2284): 330.7483658347452, (8, 2285): 330.5829819905186, (8, 2291): 328.43180701677784, (8, 2292): 328.86169313853003, (8, 2307): 330.09731982253027, (8, 2313): 328.13013440713866, (8, 2317): 328.21284572864533, (8, 2319): 329.1825131282223, (8, 2321): 329.60320381663814, (8, 2323): 329.60323323084197, (8, 2326): 331.4506520863992, (8, 2327): 331.0209317831437, (8, 2329): 330.72151343300385, (8, 2330): 330.3664248425866, (8, 2332): 331.0463434361072, (8, 2344): 330.0358400458755, (8, 2346): 329.9745483334267, (8, 2361): 330.14428092797755, (8, 2368): 334.96671111726243, (8, 2374): 335.4079431838747, (8, 2375): 335.58668261313176, (8, 2377): 333.9665910496448, (8, 2378): 335.86673738786226, (8, 2379): 335.8666052605794, (8, 2380): 336.05903899126366, (8, 2383): 334.4315406958457, (8, 2385): 334.70046083882323, (8, 2395): 334.76494331187064, (8, 2397): 335.6517221868797, (8, 2398): 333.4458524490497, (8, 2399): 334.0574686941039, (8, 2400): 333.92541442537186, (8, 2402): 334.7504069425745, (8, 2403): 335.11538345443057, (8, 2404): 335.2265988905082, (8, 2405): 334.3315420130538, (8, 2407): 335.0855333555761, (8, 2408): 335.49613636056984, (8, 2409): 334.6095857699635, (8, 2411): 335.04236451378716, (8, 2412): 334.97308192750904, (8, 2413): 335.2627870906428, (8, 2414): 334.766439398215, (8, 2422): 334.9064987525951, (8, 2424): 335.0915588961107, (8, 2426): 335.18495525127906, (8, 2433): 334.4764841141729, (8, 2436): 334.2490232072715, (8, 2437): 332.1283116592423, (8, 2440): 332.6082943670299, (8, 2445): 341.6418537027172, (8, 2447): 340.52665088870685, (8, 2454): 341.61943410358845, (8, 2455): 341.7174963498612, (8, 2460): 338.27429934710716, (8, 2461): 338.69114197983214, (8, 2471): 345.25221112043135, (8, 2492): 336.4253514104257, (8, 2511): 333.3219687622417, (8, 2523): 334.90405512175573, (8, 2525): 334.2956599403783, (8, 2535): 336.09126596316395, (8, 2537): 335.31170455926883, (8, 2538): 335.89267653014707, (8, 2539): 335.45820631113565, (8, 2540): 336.4394983602273, (8, 2542): 336.9292334548662, (8, 2559): 348.1493516136076, (8, 2575): 346.920140800904, (8, 2599): 331.17404632124806, (8, 2600): 334.69568245139465, (8, 2607): 332.8149402006127, (8, 2627): 334.595816063952, (8, 2647): 336.42152931491404, (8, 2674): 335.65998994486137, (8, 2681): 335.2572813155028, (8, 2683): 336.28560275823037, (8, 2686): 335.2311830187766, (8, 2689): 348.0755671493325, (8, 2690): 348.1074837485829, (8, 2713): 349.66611809296904, (8, 2714): 349.75267460598025, (8, 2715): 350.0778560387961, (8, 2739): 349.82817171943816, (8, 2740): 348.1399777694456, (8, 2741): 348.32710938275915, (8, 2749): 349.24070976835185, (8, 2750): 349.38904383871386, (8, 2752): 349.642005419379, (8, 2755): 349.8694220525401, (8, 2758): 349.7551024232467, (8, 2759): 349.77725557665843, (8, 2769): 349.45318458792565, (8, 2771): 348.57065638094684, (8, 2779): 348.3351452892797, (8, 2784): 344.53914263711647, (8, 2800): 344.8541008476784, (8, 2802): 347.333907341119, (8, 2803): 347.252324452554, (8, 2804): 347.0522572386583, (8, 2805): 347.4804535235297, (8, 2807): 347.5027000815965, (8, 2809): 347.28720648464963, (8, 2812): 345.31575066524937, (8, 2814): 346.89448030527257, (8, 2817): 346.5780313572387, (8, 2819): 347.64858618327196, (8, 2823): 345.14927636401495, (8, 2832): 347.82274167091697, (8, 2836): 346.37010322033353, (8, 2839): 347.5410259490242, (8, 2841): 346.84727020663996, (8, 2843): 346.80854858054266, (8, 2846): 346.48446747222414, (8, 2849): 347.97741811317115, (8, 2852): 347.67484057990276, (8, 2853): 348.1140412695137, (8, 2876): 348.06084845688963, (8, 2877): 349.1963708038068, (8, 2885): 349.1352039975268, (8, 2918): 348.081143389593, (8, 2921): 348.5327546489078, (8, 2925): 346.5424766505744, (8, 2926): 345.9495768978848, (8, 2930): 347.0705334142405, (8, 2931): 346.6472050881796, (8, 2938): 348.0154028317681, (8, 2940): 349.8073886196185, (8, 2947): 348.18534309444226, (8, 2949): 347.21875302202244, (8, 2950): 347.37320426780303, (8, 2952): 347.1240744160462, (8, 2958): 347.10502698302366, (8, 2959): 347.42479385657856, (8, 2960): 347.9478395309275, (8, 2961): 347.6513255493475, (8, 2963): 346.8547791153398, (8, 2968): 346.96987769004807, (8, 2976): 346.8319580082115, (8, 2981): 341.6122608030234, (8, 2982): 341.3906375241906, (8, 2984): 341.12544404478973, (8, 3003): 340.59908430522495, (8, 3046): 338.34298935732835, (8, 3050): 340.4208891268293, (8, 3051): 340.64695807429877, (8, 3053): 340.0699849258444, (8, 3069): 342.959132170908, (8, 3071): 340.1295161284184, (8, 3080): 348.99285609208914, (8, 3199): 339.26808348400453, (8, 3200): 338.6349097739229, (8, 3205): 342.2249036413398, (8, 3209): 338.925133869666, (8, 3215): 338.71836394340363, (8, 3217): 337.998040893139, (8, 3249): 338.8341576265738, (8, 3263): 344.29497390730756, (8, 3289): 340.68656477448747, (8, 3301): 340.7363047291039, (8, 3302): 340.5221961540671, (8, 3307): 340.2118515520158, (8, 3310): 341.04626465389833, (8, 3391): 339.2207397590535, (8, 3509): 228.22053787250098, (8, 3510): 227.71917068154744, (8, 3511): 228.1137929088808, (8, 3512): 227.85666877881857, (8, 3514): 228.00992787949482, (8, 3519): 229.0978625779251, (8, 3536): 229.21189770669272, (8, 3545): 230.05994358517634, (8, 3548): 229.36947901205383, (8, 3572): 229.42316210909692, (8, 3581): 228.61259729225264, (8, 3583): 228.52152995105664, (8, 3601): 229.94447945647914, (8, 3656): 228.89376499996163, (8, 3669): 227.3957972147921, (8, 3670): 227.8231337648297, (8, 3695): 225.473199055837, (8, 3696): 225.83732950903624, (8, 3782): 230.56645111126605, (8, 3792): 229.8634223955125, (8, 3989): 13.913977182571063, (8, 4008): 12.5, (8, 4031): 12.5, (8, 4045): 12.5, (8, 4144): 12.965400677201838, (8, 4145): 16.801906457116214, (8, 4164): 14.272419258620126, (8, 4168): 15.638062350233064, (8, 4173): 16.08013476995585, (8, 4181): 17.713272282360382, (8, 4228): 18.236161426021663, (8, 4248): 20.358910906105926, (8, 4254): 40.21659209636349, (8, 4260): 39.574583170439496, (8, 4262): 39.02188878922124, (8, 4273): 38.84520375558067, (8, 4319): 50.87936798840292, (8, 4326): 51.0379319703529, (8, 4328): 50.7508034123734, (8, 4334): 50.66845780803599, (8, 4335): 51.0008724343546, (8, 4372): 133.58813437769973, (8, 4413): 137.88713472649755, (8, 4434): 132.88778968472585, (8, 4447): 131.2064699112543, (8, 4452): 133.21318845580907, (8, 4463): 142.7922890446954, (8, 4465): 142.1129657778273, (8, 4619): 144.23975839189754, (8, 4645): 143.25802518038446, (8, 4657): 144.0292775443217, (8, 4666): 144.72533849568669, (8, 4676): 144.68562288367465, (8, 4678): 144.3156062897684, (8, 4689): 145.2477225084856, (8, 4704): 145.32855719620912, (8, 4726): 162.98883410641042, (8, 4727): 162.72216044147277, (8, 4730): 162.15505547538694, (8, 4731): 162.65383906834492, (8, 4734): 161.01961802166622, (8, 4735): 161.05787033059534, (8, 4736): 161.43690136317466, (8, 4737): 161.33284092282614, (8, 4738): 161.5957916042507, (8, 4756): 162.01580130371354, (8, 4760): 159.2684112936492, (8, 4761): 158.84666067035934, (8, 4762): 159.25474965048343, (8, 4765): 159.56881211291065, (8, 4773): 163.23398675526659, (8, 4774): 163.45990090554184, (8, 4790): 162.98687849656096, (8, 4795): 162.6374611977241, (8, 4799): 163.82086544527886, (8, 4801): 165.0141270051506, (8, 4804): 162.14640295439477, (8, 4805): 161.86611301822404, (8, 4806): 164.0421376371102, (8, 4815): 164.19434278975967, (8, 4816): 164.65142084128578, (8, 4817): 165.31604941556344, (8, 4826): 164.75441434283152, (8, 4830): 164.60344550891307, (8, 4839): 160.06380914825868, (8, 4840): 160.53068095549403, (8, 4841): 160.16150015395763, (8, 4846): 159.88784916071685, (8, 4848): 160.29255707678504, (8, 4850): 160.6110107486936, (8, 4871): 155.45067703329607, (8, 4883): 158.29456376573253, (8, 4900): 156.17159821990427, (8, 4901): 156.22100406328494, (8, 4917): 153.16992445144172, (8, 4931): 152.1232516042189, (8, 4944): 152.95217812985206, (8, 4956): 152.64989130414278, (8, 4958): 153.2863501969399, (8, 4959): 153.54638959429556, (8, 4961): 152.58789277860785, (8, 4966): 152.7838919742748, (8, 5207): 151.73430711894048, (8, 5272): 118.67123136944728, (8, 5283): 118.92916213341074, (8, 5287): 120.8754192636134, (8, 5289): 121.05544392144344, (8, 5293): 117.23934157484895, (8, 5295): 117.75341128572502, (8, 5296): 118.67707309633688, (8, 5298): 119.1879050941673, (8, 5303): 120.14982019625735, (8, 5305): 120.3545856822568, (8, 5306): 121.51807767361038, (8, 5307): 120.33846376017634, (8, 5308): 120.74093869037773, (8, 5313): 119.5691545050055, (8, 5314): 119.33794825329178, (8, 5317): 121.34479124591986, (8, 5319): 120.17794414715719, (8, 5324): 119.35691780852795, (8, 5326): 118.77701023587207, (8, 5348): 122.26844860493446, (8, 5351): 123.69940567533756, (8, 5399): 122.5328458182573, (8, 5413): 126.00012661479366, (8, 5422): 121.72151150576339, (8, 5445): 121.67568590109452, (8, 5448): 121.51094175439378, (8, 5456): 122.4529491998648, (8, 5467): 122.86814822681579, (8, 5624): 118.36263126591052, (8, 5671): 111.52399998384942, (8, 5672): 111.02509477309741, (8, 5797): 117.6530830659108, (8, 5871): 134.67968142424183, (8, 5976): 132.21382895333184, (8, 6118): 284.5372758417226, (8, 6248): 293.7570560265174, (8, 6345): 112.11823118180783, (8, 6352): 114.31561810713161, (8, 6354): 111.63689326970812, (8, 6359): 111.11214687138363, (8, 6376): 113.76090489971668, (8, 6378): 111.88460502089097, (8, 6381): 111.2262562197544, (8, 6383): 112.61908972209123, (8, 6396): 111.13027317304406, (8, 6399): 111.98117858574207, (8, 6408): 114.32284712199862, (8, 6409): 113.53718005938596, (8, 6419): 117.44828707464038, (8, 6422): 114.22333048861812, (8, 6423): 114.4133765776276, (8, 6424): 112.13826912043709, (8, 6439): 112.63802917126142, (8, 6464): 113.31918718786346, (8, 6465): 113.44601308343393, (8, 6469): 112.99081391613637, (8, 6470): 113.08300115433039, (8, 6472): 110.33671995570539, (8, 6480): 111.21759959553685, (8, 6486): 110.45016516579618, (8, 6497): 110.72234299771402, (8, 6503): 113.72664450128613, (8, 6508): 113.27170264466376, (8, 6509): 112.99492677648571, (8, 6521): 111.15271538971456, (8, 6544): 111.59354666245896, (8, 6552): 114.30359544138582, (8, 6553): 114.6676717074029, (8, 6554): 115.03452036585985, (8, 6578): 113.65507211456244, (8, 6582): 114.21272595058375, (8, 6601): 113.55020407117635, (8, 6609): 110.38702207831471, (8, 6610): 110.3458772041751, (8, 6611): 110.12191559304318, (8, 6614): 110.21832898133209, (8, 6615): 110.20425766414452, (8, 6616): 110.03285415170573, (8, 6617): 110.12384710783778, (8, 6618): 109.81054538727841, (8, 6619): 110.5068916891763, (8, 6620): 110.12405749578002, (8, 6621): 110.44543851063705, (8, 6622): 110.30630035438772, (8, 6623): 110.35173830818866, (8, 6624): 110.7200390000042, (8, 6625): 110.72574027535588, (8, 6626): 110.48403857504483, (8, 6627): 110.21402996561189, (8, 6628): 110.2892436844825, (8, 6629): 110.75496528992427, (8, 6630): 110.8387289320465, (8, 6632): 110.73173238510775, (8, 6634): 111.22476804889644, (8, 6635): 110.5001547820762, (8, 6636): 110.04989132397498, (8, 6637): 111.1800377907065, (8, 6638): 110.88851177146363, (8, 6639): 110.235162165098, (8, 6640): 110.791055725955, (8, 6641): 110.53195374460144, (8, 6642): 110.94340514213428, (8, 6643): 110.45446309372076, (8, 6645): 110.50633354489456, (8, 6646): 109.83968228668986, (8, 6647): 110.81758140325408, (8, 6653): 110.18953888909333, (8, 6655): 110.20234629149172, (8, 6658): 111.28300752718076, (8, 6662): 111.0284100640403, (8, 6819): 129.58989953335973, (8, 6996): 125.41004179849692, (8, 7059): 121.4021980455902, (8, 7187): 133.29584225232458, (8, 7304): 138.55133539460834, (8, 7528): 127.73124089373997, (8, 7720): 102.80528470865798, (8, 7793): 104.23764192568107, (8, 7807): 103.60619649468032, (8, 7808): 104.58175066165849, (8, 7831): 108.91127732953342, (8, 7850): 104.5200797450581, (8, 7852): 105.25695551350576, (8, 8012): 102.6628384302846, (8, 8125): 107.09047485934212, (8, 8208): 96.04191971988914, (8, 8392): 108.06777824947244, (8, 8651): 149.54620214904116, (8, 9088): 129.5593617255988, (8, 9443): 164.41300760021429, (8, 9444): 163.95187722924769, (8, 9828): 185.00279496180013, (8, 9868): 182.73825241295702, (8, 10180): 107.39512579385509, (8, 10256): 99.61989838820026, (8, 10276): 101.90038922757995, (8, 10378): 97.10149329545962, (8, 10676): 116.30631087622666, (8, 10714): 123.36083018572441, (8, 10730): 117.86186205191046, (8, 10862): 176.73727850587937, (8, 10881): 176.36942532086482, (8, 10883): 176.6674656340895, (8, 10885): 176.7533018991682, (8, 10891): 177.13695664755556, (8, 10909): 176.5554399199686, (8, 10911): 175.87387363352317, (8, 10913): 176.16228356927442, (8, 10915): 175.84153876787028, (8, 10919): 175.5173522273769, (8, 11037): 185.77952657490917, (8, 11039): 184.1673121395501, (8, 11516): 26.48187322936452, (8, 11856): 50.498845732151274, (8, 11857): 51.69633975307634, (8, 11861): 51.10673593803147, (8, 11881): 50.25205834062452, (8, 11902): 51.54799928295317, (8, 11911): 50.9527978085379, (8, 11914): 51.12897315679859, (8, 11922): 50.4485341173091, (8, 11924): 49.92129408759764, (8, 11926): 50.244818498244676, (8, 11950): 48.56382024807539, (8, 11963): 47.47916323887269, (8, 11983): 46.78464794744727, (8, 11985): 47.032399177367225, (8, 12009): 45.92879750468018, (8, 12010): 47.034701535187075, (8, 12018): 46.730940404015115, (8, 12020): 46.6989870805284, (8, 12021): 46.42594391157749, (8, 12024): 45.67533985420495, (8, 12025): 46.195187285807016, (8, 12027): 46.30494425329618, (8, 12031): 47.176899004969066, (8, 12032): 47.11220965212957, (8, 12035): 45.683123771621126, (8, 12041): 47.7459798348442, (8, 12045): 58.15185739627729, (8, 12145): 51.2147069011272, (8, 12275): 12.5, (8, 12294): 14.559312957080593, (8, 12358): 12.5, (8, 12463): 12.5, (8, 12465): 12.5, (8, 12482): 12.5, (8, 12503): 12.5, (8, 12506): 12.5, (8, 12549): 12.5, (8, 12559): 12.5, (8, 12569): 12.5, (8, 12572): 12.5, (8, 12574): 12.5, (8, 12576): 12.5, (8, 12591): 12.5, (8, 12608): 12.5, (8, 12696): 12.5, (8, 12710): 12.5, (8, 12728): 12.5, (8, 12766): 75.35893798746694, (8, 12771): 78.55198980816405, (8, 12790): 79.01225417564508, (8, 12795): 80.08560302152301, (8, 12797): 84.45279624546997, (8, 12798): 83.85117199206043, (8, 12811): 80.34220064874287, (8, 12830): 81.51711427882064, (8, 12848): 80.91575402066378, (8, 12850): 80.6438494040941, (8, 12852): 81.68325572711943, (8, 12854): 82.22126138169952, (8, 12859): 80.388555647546, (8, 12861): 83.25985267711094, (8, 12865): 79.68260357649562, (8, 12866): 79.95799923763036, (8, 12867): 78.88228515906283, (8, 12874): 79.403767752719, (8, 12875): 78.99644897155373, (8, 12881): 80.66658025398624, (8, 12883): 80.00156704298021, (8, 12885): 78.6436582276422, (8, 12888): 80.30830184803601, (8, 12889): 80.4586515632797, (8, 12892): 79.28938267260071, (8, 12893): 80.28526098333711, (8, 12896): 79.9634352851204, (8, 12906): 79.38746167606863, (8, 13018): 84.79863393276405, (8, 13071): 84.99753376002771, (8, 13131): 88.5525570276918, (8, 13146): 84.97259458369315, (8, 13159): 90.6217393359907, (8, 13193): 89.21773964150128, (8, 13198): 95.39286172896453, (8, 13292): 88.27827007647076, (8, 13296): 86.39537595560861, (8, 13406): 99.31771601488596, (8, 13407): 99.53715587478474, (8, 13417): 100.19965793645756, (8, 13418): 99.57642172971981, (8, 13438): 96.6862367896854, (8, 13442): 96.09181158813436, (8, 13443): 96.6199273754895, (8, 13764): 144.7451960090385, (8, 13766): 144.06332220628056, (8, 13771): 144.94550438829043, (8, 13783): 144.97356217212962, (8, 13784): 143.22905578935834, (8, 13792): 146.60307092469475, (8, 13824): 145.48091089855168, (8, 14017): 140.4806882157492, (8, 14870): 163.75981465564718, (8, 14997): 136.5974449798881, (8, 15000): 136.7096890304164, (8, 15003): 136.47337322613396, (8, 15006): 134.78175682792826, (8, 15007): 134.3802229931314, (8, 15056): 134.95579166828398, (8, 15063): 135.4323493951916, (8, 15069): 135.77543816941713, (8, 15076): 134.43548838527218, (8, 15086): 135.5344917202275, (8, 15087): 136.22245962892399, (8, 15111): 137.31628907618037, (8, 15116): 136.70422047422963, (8, 15722): 147.7802123423971, (8, 15998): 159.71839736334314, (8, 16073): 241.29440945928226, (8, 16939): 307.20169921709095, (8, 16940): 306.567282278051, (8, 16951): 307.14955280888245, (8, 16963): 307.24522847096665, (8, 16965): 308.07883294756874, (8, 16969): 307.8032023248964, (8, 16970): 307.5742297146364, (8, 16971): 306.8282901041777, (8, 16973): 306.7277751322081, (8, 16974): 308.36561742665515, (8, 16976): 307.6638541007024, (8, 16978): 307.13648908346016, (8, 16980): 307.98213173327804, (8, 16982): 308.30705792427426, (8, 17045): 326.2886949322713, (8, 17048): 327.2177251365185, (8, 17304): 25.597417484251313, (8, 17305): 25.211253124684834, (8, 17330): 25.077639857962318, (8, 17334): 26.477948025902325, (8, 17343): 24.36091750702449, (8, 17345): 25.70754947710489, (8, 17347): 24.619395635021256, (8, 17351): 27.49450740679842, (8, 17372): 26.253285190159534, (8, 17373): 24.52897389273734, (8, 17377): 24.34125558814694, (8, 17382): 25.295531001595712, (8, 17383): 25.38736189657461, (8, 17389): 25.8845462326121, (8, 17400): 25.050579937120485, (8, 17401): 25.201372910159275, (8, 17402): 24.915033726025914, (8, 17403): 24.754013878035053, (8, 17440): 24.84686874326659, (8, 17455): 24.008195218058756, (8, 17491): 23.36369267533992, (8, 17507): 29.051524442823066, (8, 17509): 28.82748783877441, (8, 17590): 26.9877225833689, (8, 17615): 35.11897634270237, (8, 17642): 34.187387825049626, (8, 17643): 33.86961074924131, (8, 17668): 35.36641625638886, (8, 17721): 38.533592346109884, (8, 17754): 35.32804432561339, (8, 17769): 29.979881531580208, (8, 17776): 30.174496871481885, (8, 17804): 29.44551981786942, (8, 17809): 29.01934356256366, (8, 17824): 29.941058833347846, (8, 17837): 28.42097828168695, (8, 17838): 27.887420306411993, (8, 17862): 28.02483511318609, (8, 17866): 27.223064467473645, (8, 17872): 28.655465620923813, (8, 17873): 29.187124230020263, (8, 17881): 28.312703208902164, (8, 17947): 255.71976356717758, (8, 17951): 254.42841959498844, (8, 17953): 254.20647307375015, (8, 17954): 254.31297209374253, (8, 17959): 255.41186095101412, (8, 17963): 254.91296059157787, (8, 18000): 248.41160138207678, (8, 18001): 248.7047783927181, (8, 18111): 267.83253667715843, (8, 18148): 235.52915913731664, (8, 18166): 248.1579144823723, (8, 18189): 259.67613851318237, (8, 18239): 24.595989934392158, (8, 18240): 24.509639520673364, (8, 18245): 24.502919020489415, (8, 18247): 24.51156490086839, (8, 18251): 24.392953718039454, (8, 18256): 24.158137389692946, (8, 18258): 24.22871050408003, (8, 18259): 24.15813616328751, (8, 18260): 24.042818866171995, (8, 18262): 23.88955451779693, (8, 18263): 24.074303227411907, (8, 18264): 23.9649205711386, (8, 18266): 23.77375231343774, (8, 18267): 23.680036025009038, (8, 18268): 23.60107924976897, (8, 18269): 23.40543214408509, (8, 18275): 23.497293024006357, (8, 18285): 24.03779932603141, (8, 18308): 26.12919519060738, (8, 18313): 26.574284612679445, (8, 18314): 26.07676348810122, (8, 18315): 23.66008451265477, (8, 18316): 23.554183331479553, (8, 18317): 23.454982433452813, (8, 18320): 23.53364826407487, (8, 18321): 23.425113290509742, (8, 18322): 23.29277613789356, (8, 18324): 23.3549473029746, (8, 18325): 23.109085873730784, (8, 18326): 23.206191680262087, (8, 18327): 23.266309997514043, (8, 18329): 23.13487845382028, (8, 18330): 22.88357574661397, (8, 18331): 23.10698293943573, (8, 18332): 23.27617397193296, (8, 18333): 23.014729773005584, (8, 18336): 23.332259465661032, (8, 18337): 23.326368800152164, (8, 18403): 22.789421820997813, (8, 18432): 23.756424567636103, (8, 18451): 22.895997168875283, (8, 18466): 23.192043399135663, (8, 18481): 23.91918422633145, (8, 18483): 23.832039901787947, (8, 18484): 24.033368730184137, (8, 18485): 24.729760752366996, (8, 18486): 24.694458653483167, (8, 18487): 25.11465170606703, (8, 18489): 24.423752981725297, (8, 18490): 24.361358053019565, (8, 18491): 24.216469866979516, (8, 18492): 25.348448787737226, (8, 18493): 24.856272095978078, (8, 18494): 24.41086731436179, (8, 18495): 24.483229247280804, (8, 18496): 24.56026916369702, (8, 18497): 25.297099025503503, (8, 18498): 24.85292927555199, (8, 18499): 24.59166973342567, (8, 18501): 24.94173050503262, (8, 18502): 25.119188562068526, (8, 18503): 25.144290174260465, (8, 18504): 24.387837354034982, (8, 18506): 25.183188075972314, (8, 18507): 25.405495053779752, (8, 18508): 24.716336471710903, (8, 18509): 24.799944272181413, (8, 18510): 25.267623862727625, (8, 18511): 24.997149157853887, (8, 18512): 25.015058997831723, (8, 18515): 24.501521576743247, (8, 18516): 24.793330124956487, (8, 18517): 25.151876468007963, (8, 18518): 24.574752257919936, (8, 18519): 24.29979528867397, (8, 18520): 24.656777397809957, (8, 18522): 23.425959409852723, (8, 18523): 23.490579833082112, (8, 18532): 23.41350237808171, (8, 18535): 23.67707648123355, (8, 18537): 23.826572165486127, (8, 18539): 23.846055847819002, (8, 18540): 23.88281719522029, (8, 18541): 23.85515601394529, (8, 18542): 23.828703600939253, (8, 18543): 24.003500262979482, (8, 18546): 24.088130367773886, (8, 18555): 23.87111636675679, (8, 18556): 23.90206102462464, (8, 18565): 23.56625884331965, (8, 18567): 23.705284497728638, (8, 18568): 23.734944660933035, (8, 18577): 22.88884164946863, (8, 18583): 22.730416936521983, (8, 18605): 22.203155351936573, (8, 18608): 24.054673881042063, (8, 18616): 21.46833112064783, (8, 18618): 21.117830788891084, (8, 18625): 20.45143238205131, (8, 18645): 20.684939876582142, (8, 18646): 20.790365356327385, (8, 18653): 22.083364902979163, (8, 18654): 21.618995641039433, (8, 18655): 22.086079216684595, (8, 18666): 18.83004644741409, (8, 18837): 17.191601605739454, (8, 18974): 21.421145918651728, (8, 18999): 19.954588840384908, (8, 19000): 19.62212578968336, (8, 19174): 36.64049992375871, (8, 19342): 29.966253333793542, (8, 19455): 33.367059163167504, (8, 19555): 51.46420197894168, (8, 19564): 50.822781629466114, (8, 19573): 51.477399368129, (8, 19586): 51.74398166075981, (8, 19605): 51.38110479821973, (8, 19611): 50.90186616341376, (8, 19614): 51.01116546083568, (8, 19641): 42.4863498124171, (8, 19702): 42.847317237534895, (8, 19713): 43.41109270437355, (8, 19731): 54.4329444224271, (8, 19819): 36.022105973117974, (8, 19893): 84.50609541152077, (8, 19899): 85.66157766467303, (8, 19929): 83.98496719723686, (8, 19951): 83.75560494886695, (8, 19962): 85.43159988611404, (8, 19970): 82.22295926729333, (8, 19971): 82.93353837757451, (8, 19972): 83.50567670278413, (8, 19975): 83.03519022096047, (8, 19978): 80.38902211336627, (8, 19987): 79.88301905644502, (8, 19989): 79.90164532900658, (8, 20039): 79.64072891628574, (8, 20043): 78.95152313438, (8, 20047): 78.31982962942233, (8, 20052): 78.91747748049605, (8, 20054): 79.23762496076138, (8, 20085): 74.92210890506182, (8, 20104): 74.83896117440666, (8, 20132): 76.18739718350756, (8, 20203): 91.05763365475141, (8, 20280): 93.27188816827086, (8, 20285): 94.18776684457893, (8, 20290): 92.81545722526998, (8, 20297): 92.73915601331966, (8, 20309): 85.79557032422753, (8, 20453): 81.39805424082729, (8, 20485): 92.7025583632282, (8, 20520): 92.63068219616507, (8, 20526): 94.84725223490416, (8, 20698): 168.39707064238328, (8, 20868): 192.66913755336273, (8, 21042): 84.02623502679181, (8, 21057): 79.21623625823835, (8, 21066): 81.93717606020354, (8, 21075): 82.32114399411525, (8, 21093): 84.16916391804334, (8, 21098): 81.57474501033064, (8, 21127): 83.89583686332422, (8, 21130): 83.2440598991696, (8, 21144): 82.89973298722488, (8, 21146): 84.20643993694055, (8, 21147): 82.84096383416271, (8, 21148): 82.17285080126024, (8, 21153): 82.52733372550794, (8, 21293): 76.78633102298507, (8, 21426): 74.2978515442303, (8, 21442): 68.77027202507914, (8, 21451): 68.25108725605801, (8, 21466): 71.65000499088637, (8, 21469): 70.93641254124414, (8, 21471): 72.00767173905844, (8, 21473): 71.44433006308967, (8, 21475): 71.9778202444422, (8, 21482): 70.39522296052944, (8, 21484): 70.59120247098477, (8, 21488): 70.98563780276326, (8, 21494): 72.1115608621449, (8, 21498): 71.54781729434576, (8, 21500): 72.54819187219441, (8, 21514): 71.65513252401469, (8, 21537): 73.03961800332866, (8, 21662): 71.49696750419345, (8, 21691): 74.35040959264448, (8, 21757): 78.326243579901, (8, 21777): 94.82387921174448, (8, 21778): 95.5187065382686, (8, 21779): 95.3931030529754, (8, 21790): 93.76091722594855, (8, 21802): 94.31141162612714, (8, 21824): 93.86354707641534, (8, 21874): 95.54387686578526, (8, 21879): 96.45729402253232, (8, 21983): 90.91749777770644, (8, 22002): 85.23288582544211, (8, 22132): 84.98287803191552, (8, 22261): 194.9607660158502, (8, 22298): 193.74929278781212, (8, 22339): 203.30220655461483, (8, 22508): 180.23463808297862, (8, 22841): 329.68328225418725, (8, 22842): 329.76795905407, (8, 22874): 328.2531579939386, (8, 22941): 328.16160036029675, (8, 22956): 329.3258573042975, (8, 22960): 329.45421653188686, (8, 22968): 331.6274990114685, (8, 22970): 331.77266209707454, (8, 22974): 332.986529697845, (8, 22980): 334.3106194311524, (8, 23025): 335.1219188852198, (8, 23028): 335.0179211440526, (8, 23081): 338.3748266803851, (8, 23104): 337.4776272547202, (8, 23147): 323.24894303091537, (8, 23298): 60.35179661651624, (8, 23376): 62.471023225323755, (8, 23381): 64.94299332018568, (8, 23529): 60.01934337904126, (8, 23556): 61.06404357689862, (8, 23718): 60.774577544032745, (8, 24001): 47.623597726988464, (8, 24094): 46.36876913992704, (8, 24129): 44.39851966679795, (8, 24174): 49.6785999606082, (8, 24235): 46.274141447190885, (8, 24259): 43.57706591713108, (8, 24260): 43.84832437677949, (8, 24261): 44.12548193791184, (8, 24305): 41.055234761554736, (8, 24306): 40.88078543737177, (8, 24307): 41.31596564097329, (8, 24308): 41.12916653959652, (8, 24498): 33.63314427214397, (8, 24499): 33.652312714501264, (8, 24500): 33.94049364596529, (8, 24668): 33.766911656492944, (8, 24711): 32.82573363650589, (8, 24756): 33.039242293084804, (8, 24788): 31.954987373120886, (8, 24809): 35.257293288426276, (8, 24813): 34.106875389445484, (8, 24821): 34.43018868101505, (8, 24825): 34.42670639247697, (8, 24832): 35.29259172362476, (8, 24833): 34.92437935023436, (8, 24835): 34.62995697710825, (8, 24837): 33.87688402965486, (8, 24840): 35.43548252932827, (8, 24841): 34.6886107622076, (8, 24844): 35.53551698305017, (8, 24845): 34.74629704524837, (8, 24846): 35.42044036932462, (8, 24849): 35.277865678653534, (8, 24850): 34.13650734850484, (8, 24863): 38.508751485510814, (8, 24866): 37.79768556675008, (8, 24885): 37.363376886500774, (8, 24886): 37.54425340300873, (8, 24889): 35.22579880929039, (8, 24903): 34.290114275034504, (8, 24909): 36.22312713371103, (8, 24999): 12.5, (8, 25019): 12.5, (8, 25028): 12.5, (8, 25137): 101.94831523344324, (8, 25145): 101.47038709882025, (8, 25208): 105.05064941494268, (8, 25233): 105.83064874127562, (8, 25371): 96.55450841141904, (8, 25377): 96.33865258681722, (8, 25828): 121.91521204424393, (8, 25851): 124.23391342531824, (8, 25874): 120.40379903814573, (8, 25898): 120.91875931467857, (8, 25946): 122.23707486066742, (8, 26047): 118.23571053948052, (8, 26066): 94.93700754657138, (8, 26197): 107.81772145446473, (8, 26212): 145.44957493087392, (8, 26253): 147.81118823932854, (8, 26254): 146.74399674064188, (8, 26257): 146.4553699042101, (8, 26258): 147.492032903409, (8, 26260): 146.91858298031872, (8, 26266): 146.60433241781783, (8, 26267): 146.10984994277788, (8, 26271): 146.23590395666565, (8, 26304): 137.39219434754372, (8, 26305): 137.07488786819965, (8, 26363): 126.50051702667659, (8, 26441): 200.68477828001937, (8, 26442): 200.44014654305514, (8, 26450): 199.24638493708792, (8, 26459): 199.15133129579723, (8, 26462): 199.3170591489367, (8, 26467): 202.8202639561608, (8, 26471): 201.83948080906566, (8, 26472): 201.7357458593144, (8, 26473): 201.69567485273078, (8, 26476): 201.1361239116597, (8, 26485): 199.74691614792889, (8, 26493): 199.78403404387723, (8, 26524): 199.84105505165124, (8, 26525): 199.70460985941983, (8, 26556): 201.36566340654312, (8, 26560): 201.24737930987857, (8, 26561): 200.48935397281886, (8, 26564): 201.04295057411093, (8, 26569): 200.30616154631076, (8, 26570): 200.00606332839786, (8, 26573): 200.20131918567276, (8, 26581): 200.17690298377786, (8, 26583): 199.91338006573451, (8, 26593): 200.1891224803612, (8, 26837): 203.06124318348222, (8, 26844): 203.85982115005925, (8, 26863): 202.12883553458207, (8, 26893): 204.43063939983787, (8, 26902): 205.51564116864864, (8, 26905): 204.41043957283398, (8, 26912): 205.2596141117572, (8, 26921): 203.2309796974038, (8, 26922): 201.0654808524223, (8, 27212): 207.87002885280575, (8, 27218): 206.850973975228, (8, 27239): 209.4265692024365, (8, 27257): 208.6380427827486, (8, 27274): 209.74961699990666, (8, 27279): 209.59442952674263, (8, 27282): 208.68290109006844, (8, 27283): 209.0094473132408, (8, 27285): 210.172600429267, (8, 27286): 209.36660174210127, (8, 27290): 207.9065131784603, (8, 27295): 207.31932608464106, (8, 27300): 209.90005563772854, (8, 27344): 207.53555889054613, (8, 27366): 208.58316840052373, (8, 27383): 210.28717811613913, (8, 27398): 211.3583482340522, (8, 27406): 210.43929795083065, (8, 27407): 210.69468182511278, (8, 27426): 209.37600339983322, (8, 27432): 205.47071719106054, (8, 27460): 207.8994198989878, (8, 27523): 209.1133822571343, (8, 27545): 225.0179764633645, (8, 27602): 245.86070584216074, (8, 27606): 246.22111238529826, (8, 27646): 224.81730871936662, (8, 27667): 228.97051350583493, (8, 27672): 229.1790147716468, (8, 27674): 228.47685760879, (8, 27688): 229.0323009749954, (8, 27692): 229.90788157787105, (8, 27693): 229.2881447610273, (8, 27705): 229.26582596003837, (8, 27712): 229.5791274882232, (8, 27786): 246.09504780798923, (8, 27790): 243.42524030347678, (8, 27791): 243.17819657478148, (8, 27795): 244.95050836440248, (8, 27801): 242.99598419798784, (8, 27813): 246.77229029874837, (8, 27816): 245.9512589424151, (8, 27823): 242.91869635336934, (8, 27830): 244.9581537297785, (8, 27884): 217.99516502534087, (8, 27885): 223.0902598227023, (8, 27896): 220.0061255964909, (8, 27919): 219.78437417670202, (8, 27922): 220.43304036783283, (8, 27930): 218.7581983142, (8, 27934): 218.96194182457234, (8, 27935): 219.11572944589074, (8, 27948): 244.19980810477162, (8, 27951): 245.24532937985603, (8, 28061): 223.5335701025705, (8, 28290): 267.5102401953612, (8, 28292): 268.27270281747803, (8, 28293): 267.64861038553346, (8, 28295): 267.1887510357081, (8, 28296): 267.4205982795351, (8, 28297): 267.09469360040157, (8, 28302): 266.70409838557276, (8, 28310): 271.2947508569145, (8, 28313): 271.5656290720437, (8, 28372): 272.4505003762987, (8, 28398): 272.4635199018512, (8, 28399): 272.1304064416458, (8, 28400): 272.57162162017084, (8, 28401): 271.50890821572887, (8, 28445): 270.9090969213169, (8, 28475): 271.14798439572115, (8, 28885): 52.50270865014551, (8, 28886): 53.08886768504812, (8, 28915): 53.992021568931854, (8, 28916): 53.868155786820374, (8, 28917): 54.2809795714844, (8, 28921): 51.6930100562149, (8, 28931): 52.08036123517524, (8, 28945): 57.511091968867035, (8, 28982): 55.82593695205098, (8, 29219): 61.10526386818903, (8, 29228): 61.86634431664264, (8, 29246): 61.71387521594194, (8, 29248): 63.261208471614225, (8, 29282): 63.333597265215175, (8, 29290): 59.96964465478248, (8, 29291): 60.4637287047957, (8, 29292): 60.21784278887755, (8, 29293): 60.31160343705631, (8, 29294): 60.8766541603805, (8, 29298): 60.70056343890225, (8, 29299): 61.11227611392759, (8, 29304): 60.32652226015592, (8, 29317): 60.1489367254898, (8, 29323): 60.09627439353836, (8, 29330): 60.23028354909696, (8, 29331): 59.97745097949607, (8, 29344): 63.772587517097456, (8, 29445): 79.10966327992645, (8, 29724): 322.83685347087686, (8, 29738): 323.1960449101833, (8, 29745): 321.9989937170399, (8, 29748): 321.44594412168954, (8, 29750): 321.71111364961047, (8, 29759): 321.04727625022855, (8, 29772): 322.3619170136872, (8, 29781): 322.0529867424586, (8, 29784): 322.15427535148785, (8, 29790): 322.20498914263936, (8, 29811): 321.1177644881445, (8, 29817): 321.5361655174041, (8, 29818): 321.2217842382919, (8, 29929): 322.34445534954017, (8, 30039): 329.0885135966892, (8, 30066): 327.2322970172645, (8, 30116): 313.45965721148315, (8, 30238): 293.19018736898323, (8, 30248): 305.25629131393447, (8, 30260): 305.66350293298166, (8, 30545): 53.516594418747346, (8, 30733): 68.07541231246621, (8, 30756): 76.26667652464728, (8, 30921): 66.77574184351836, (8, 31079): 109.71359235132044, (8, 31149): 111.1082386750739, (8, 31154): 111.20981954075386, (8, 31160): 111.23397313792246, (8, 31163): 111.5035103660548, (8, 31189): 119.02350430605168, (8, 31215): 118.68046611503492, (8, 31259): 120.28528031445799, (8, 31262): 121.04161435251334, (8, 31430): 109.6865794198945, (8, 31568): 132.31295674260699, (8, 31751): 114.26796851823681, (11, 109): 45.54123545574518, (11, 872): 230.2726575565086, (11, 873): 231.20649237046612, (11, 877): 230.9456641046789, (11, 879): 231.09289516898474, (11, 884): 230.3552066948116, (11, 889): 230.89776369082188, (11, 891): 230.02223900809665, (11, 892): 231.79821769222997, (11, 894): 231.64370889973236, (11, 896): 230.59538194456485, (11, 903): 231.08295731551078, (11, 909): 229.19929353106653, (11, 910): 229.49017110271467, (11, 912): 228.8920927861034, (11, 913): 228.2637109949668, (11, 916): 227.87623583693212, (11, 926): 229.68737800050772, (11, 927): 229.3552839766223, (11, 948): 229.66937967354383, (11, 961): 229.8480950592719, (11, 962): 229.89615730990803, (11, 963): 229.9688716933364, (11, 967): 231.44136168738933, (11, 974): 231.1494189012457, (11, 998): 231.88439732018472, (11, 1014): 251.22087827618466, (11, 1086): 225.54694059175654, (11, 1087): 225.12712856630506, (11, 1089): 224.42536231126212, (11, 1090): 224.84313959517684, (11, 1092): 226.18756675541033, (11, 1097): 225.22178125480775, (11, 1107): 226.6657582013706, (11, 1387): 84.64844892845893, (11, 1554): 72.20058424025099, (11, 1827): 274.66148121789473, (11, 1828): 274.72344792262993, (11, 1829): 274.89168337388804, (11, 1830): 274.9178254809659, (11, 1831): 274.9705010317533, (11, 1832): 274.85333840891246, (11, 1833): 274.83477451965473, (11, 1836): 274.69369132400226, (11, 1841): 275.3350843029299, (11, 1843): 275.084723880217, (11, 1844): 275.2257557373021, (11, 1845): 274.953667481666, (11, 1847): 273.901239649618, (11, 1848): 274.24429000031773, (11, 1849): 275.88131770333115, (11, 1850): 276.02217522569623, (11, 1851): 274.5861104580859, (11, 1852): 274.6797414747116, (11, 1854): 274.7896380306511, (11, 1856): 273.94364365784804, (11, 1857): 274.25846576672114, (11, 1858): 275.67745481339495, (11, 1861): 274.9294083235983, (11, 1866): 273.9813204194472, (11, 1867): 275.29430194368166, (11, 1868): 275.03698802066947, (11, 1870): 275.2867461028739, (11, 1871): 275.1909291237292, (11, 1875): 274.72587137320636, (11, 1880): 274.0957475464915, (11, 1882): 274.2947423306317, (11, 1883): 275.9571504322821, (11, 1889): 274.15796032821106, (11, 1893): 274.79734719273233, (11, 1894): 274.54064279637714, (11, 1899): 273.9016752642421, (11, 1900): 274.0527596505623, (11, 1902): 275.20855541605624, (11, 1905): 275.55935208175464, (11, 1907): 274.4030504510573, (11, 1910): 274.43052484045563, (11, 1917): 275.97736691718325, (11, 1920): 274.3651606678468, (11, 1935): 275.46842784952497, (11, 1937): 275.751513796529, (11, 1946): 273.2187330260627, (11, 1949): 273.472407356322, (11, 1950): 272.63271371468716, (11, 1951): 273.0761705732614, (11, 1952): 273.6217920356293, (11, 1953): 273.61503866313114, (11, 1954): 273.5060600801419, (11, 1958): 273.46535545123936, (11, 1960): 274.00027483185903, (11, 1968): 274.21093226091506, (11, 1969): 275.3934723054578, (11, 1974): 275.09638253114133, (11, 1975): 275.13790662035984, (11, 1979): 274.3584128097966, (11, 1980): 274.4402976204681, (11, 1981): 274.5562755870818, (11, 1985): 274.68444844666436, (11, 1994): 272.55353992209183, (11, 2011): 274.32871849733044, (11, 2019): 276.935573431042, (11, 2020): 276.5919601919273, (11, 2029): 275.4190733626981, (11, 2030): 276.35165400720933, (11, 2032): 275.2955275030896, (11, 2033): 275.85186259542604, (11, 2034): 275.9075718518973, (11, 2036): 274.98855694050366, (11, 2037): 275.21312586204687, (11, 2038): 275.00348588571376, (11, 2042): 278.75168070530026, (11, 2050): 275.585991037157, (11, 2051): 275.6038978535166, (11, 2053): 275.6717804028153, (11, 2054): 276.00587846324026, (11, 2066): 275.33865197570935, (11, 2067): 275.3039343630233, (11, 2071): 271.8929234925841, (11, 2072): 272.4564198850162, (11, 2073): 270.57658903122564, (11, 2074): 270.53932230305503, (11, 2080): 269.61492610204465, (11, 2082): 272.7765724990769, (11, 2083): 273.06358013052187, (11, 2089): 272.33830738982647, (11, 2090): 272.5936552302073, (11, 2092): 272.14950057610207, (11, 2098): 269.9187696314655, (11, 2099): 270.31930859627465, (11, 2101): 269.9184124043023, (11, 2102): 271.5063349639303, (11, 2103): 271.03321502632, (11, 2104): 270.8049092234803, (11, 2106): 273.3058756894947, (11, 2112): 270.1895997512854, (11, 2113): 271.7720706076044, (11, 2114): 272.26647591433897, (11, 2117): 273.60152849047904, (11, 2123): 268.65897109423014, (11, 2124): 268.98618832710423, (11, 2134): 268.2312488870222, (11, 2138): 269.12309891967595, (11, 2141): 268.29007403714735, (11, 2148): 269.45475637664924, (11, 2150): 267.526576512115, (11, 2151): 267.9214532150962, (11, 2152): 267.3925073010372, (11, 2153): 269.50002734280116, (11, 2154): 268.1009362826211, (11, 2155): 268.06055269360627, (11, 2156): 267.72538664499086, (11, 2157): 268.49120330404014, (11, 2160): 269.9116401435262, (11, 2161): 267.4043156879241, (11, 2162): 269.81635879204725, (11, 2163): 269.3334865756738, (11, 2164): 269.3442225761298, (11, 2168): 268.0115133554461, (11, 2172): 268.6316360491114, (11, 2174): 267.9684076216058, (11, 2178): 268.99237055262086, (11, 2179): 268.80652836891966, (11, 2183): 269.18035618853776, (11, 2185): 269.24350485244287, (11, 2186): 268.95969668857146, (11, 2190): 269.9007093275339, (11, 2192): 269.4043920035205, (11, 2193): 269.24832168112016, (11, 2194): 268.7416228837546, (11, 2195): 268.75961742940837, (11, 2197): 269.5576457948265, (11, 2205): 268.97746487673726, (11, 2207): 268.1938268609098, (11, 2208): 268.6502725166972, (11, 2212): 269.19610306525726, (11, 2214): 260.6110733200721, (11, 2225): 262.056594592921, (11, 2231): 257.7753805952471, (11, 2278): 267.58136805415495, (11, 2284): 268.7506641121898, (11, 2285): 268.66612385756395, (11, 2291): 267.0217680940243, (11, 2292): 266.7733961690749, (11, 2307): 268.09609202351874, (11, 2313): 266.92746292246756, (11, 2317): 265.8254106550786, (11, 2319): 267.1726044619338, (11, 2321): 267.72126065527067, (11, 2323): 267.526896583147, (11, 2326): 269.0756920495833, (11, 2327): 268.63064260274797, (11, 2329): 268.340534235335, (11, 2330): 268.0412704692656, (11, 2332): 268.8364697809306, (11, 2344): 267.5112327271175, (11, 2346): 267.58292398617823, (11, 2361): 266.63557966144873, (11, 2368): 272.27447180431255, (11, 2374): 272.83604459282213, (11, 2375): 272.9541047911169, (11, 2377): 271.1717322433276, (11, 2378): 273.30293353655594, (11, 2379): 273.43878485367657, (11, 2380): 273.54271753245104, (11, 2383): 271.5732313062867, (11, 2385): 271.80599189834305, (11, 2395): 271.75313969310196, (11, 2397): 273.2762785668242, (11, 2398): 270.6141244507855, (11, 2399): 271.1906293033394, (11, 2400): 271.0497838692134, (11, 2402): 272.29213566524294, (11, 2403): 272.6837007140797, (11, 2404): 272.74677312781466, (11, 2405): 271.8371184800841, (11, 2407): 272.5233425275368, (11, 2408): 273.02203120320513, (11, 2409): 272.0986209839367, (11, 2411): 272.8339931882765, (11, 2412): 272.6738682648606, (11, 2413): 273.01605581240364, (11, 2414): 272.5147276940447, (11, 2422): 272.76816212954714, (11, 2424): 272.7507832075821, (11, 2426): 272.8044287885325, (11, 2433): 272.13593274560066, (11, 2436): 272.0424756371061, (11, 2437): 269.73457811040925, (11, 2440): 270.21587526037166, (11, 2445): 281.1036281202627, (11, 2447): 279.7817396325469, (11, 2454): 280.94350035129855, (11, 2455): 280.9366998847579, (11, 2460): 277.42432575108035, (11, 2461): 277.87348248294046, (11, 2471): 285.45546215851334, (11, 2492): 280.54920711431566, (11, 2511): 276.52540651107273, (11, 2523): 278.59361031523565, (11, 2525): 278.1978954960129, (11, 2535): 277.7178924641699, (11, 2537): 276.97162802976544, (11, 2538): 277.4185372353741, (11, 2539): 277.5233319618368, (11, 2540): 278.065008120882, (11, 2542): 278.7225269130007, (11, 2559): 289.1394027796903, (11, 2575): 288.5332897092591, (11, 2599): 270.7674022307825, (11, 2600): 274.7608949435029, (11, 2607): 272.1919714952119, (11, 2627): 279.8846668463995, (11, 2647): 282.18732124095646, (11, 2674): 280.76687688864115, (11, 2681): 280.64751412507667, (11, 2683): 281.5872896786339, (11, 2686): 280.3376085516335, (11, 2689): 294.05316689982203, (11, 2690): 294.1598373331376, (11, 2713): 297.9948150800173, (11, 2714): 298.38711977129367, (11, 2715): 298.71231863983456, (11, 2739): 298.3754558947939, (11, 2740): 295.8639568131611, (11, 2741): 295.99321950746156, (11, 2749): 298.0989568796704, (11, 2750): 298.1425491986374, (11, 2752): 298.34819001046935, (11, 2755): 298.6425004641168, (11, 2758): 298.6163090239322, (11, 2759): 298.5912533111286, (11, 2769): 298.1463979296673, (11, 2771): 296.5098035413634, (11, 2779): 297.03769112620057, (11, 2784): 293.5425585934514, (11, 2800): 294.6189551189237, (11, 2802): 295.4599065688492, (11, 2803): 295.28197449405144, (11, 2804): 295.04219416588376, (11, 2805): 295.8969325296636, (11, 2807): 295.82236385110605, (11, 2809): 295.8213753596175, (11, 2812): 293.58377546095267, (11, 2814): 296.06792734879696, (11, 2817): 296.6200227242007, (11, 2819): 295.7323858334289, (11, 2823): 294.2548233980444, (11, 2832): 296.3802302344999, (11, 2836): 294.8978568828839, (11, 2839): 295.76269722627865, (11, 2841): 296.45006243002723, (11, 2843): 296.254223999617, (11, 2846): 295.40814305760995, (11, 2849): 296.7025575208122, (11, 2852): 296.3314314833447, (11, 2853): 296.8766947815465, (11, 2876): 297.27726523339805, (11, 2877): 298.5030689642433, (11, 2885): 299.3697704692146, (11, 2918): 295.5523980461209, (11, 2921): 296.12991987556, (11, 2925): 293.24065802743496, (11, 2926): 292.1722522128163, (11, 2930): 294.86271734682066, (11, 2931): 293.61403595008323, (11, 2938): 295.65390429757144, (11, 2940): 296.6952494847176, (11, 2947): 294.8219602162338, (11, 2949): 294.63244312378015, (11, 2950): 294.956770694171, (11, 2952): 294.70606412528196, (11, 2958): 294.6181001776466, (11, 2959): 294.753942738802, (11, 2960): 295.35492259228744, (11, 2961): 295.1267353241083, (11, 2963): 294.4576279896562, (11, 2968): 294.67456821210317, (11, 2976): 294.33333295162, (11, 2981): 290.1983477953253, (11, 2982): 290.1716340267348, (11, 2984): 289.9482224097926, (11, 3003): 289.63395177687846, (11, 3046): 285.09222205273807, (11, 3050): 288.26504020705283, (11, 3051): 288.41930570807534, (11, 3053): 287.91688352790703, (11, 3069): 291.1738287890562, (11, 3071): 287.52733433667873, (11, 3080): 299.559664097834, (11, 3199): 289.50041694749933, (11, 3200): 288.9989157019485, (11, 3205): 292.48799020401844, (11, 3209): 289.3125827519008, (11, 3215): 288.9730888607805, (11, 3217): 288.280629270718, (11, 3249): 288.971375084739, (11, 3263): 294.1734269428588, (11, 3289): 290.4487026512316, (11, 3301): 290.77546979149366, (11, 3302): 290.46685141712385, (11, 3307): 290.1388879369603, (11, 3310): 291.073768271324, (11, 3391): 294.72964088400283, (11, 3509): 175.19801758854626, (11, 3510): 174.69760961247712, (11, 3511): 174.9366838657689, (11, 3512): 174.54455961797834, (11, 3514): 174.57503592602438, (11, 3519): 176.8312698875405, (11, 3536): 175.91534471555238, (11, 3545): 176.6059346265818, (11, 3548): 175.71520379523932, (11, 3572): 176.3137678618831, (11, 3581): 176.02088841782097, (11, 3583): 175.29312162418464, (11, 3601): 177.91609368789702, (11, 3656): 177.46333856118488, (11, 3669): 177.26262009748524, (11, 3670): 177.74369240645075, (11, 3695): 174.85807873221748, (11, 3696): 175.19840819694144, (11, 3782): 174.26196637125295, (11, 3792): 173.96075830967683, (11, 3989): 80.2399353831597, (11, 4008): 82.81936106279788, (11, 4031): 83.91034838686012, (11, 4045): 81.79355574875052, (11, 4144): 80.75283473655831, (11, 4145): 76.86426541633847, (11, 4164): 79.44875651494874, (11, 4168): 78.03892149157281, (11, 4173): 77.57340673846316, (11, 4181): 76.00223249634402, (11, 4228): 75.91006298199696, (11, 4248): 73.39700169331512, (11, 4254): 53.55654242664925, (11, 4260): 54.279100925202286, (11, 4262): 54.723698685896885, (11, 4273): 54.9603522585348, (11, 4319): 43.094509493546965, (11, 4326): 42.987719204753674, (11, 4328): 43.295205825600775, (11, 4334): 43.24594981280941, (11, 4335): 42.91288599368834, (11, 4372): 45.53205889080432, (11, 4413): 52.96361185628558, (11, 4434): 44.75582827761256, (11, 4447): 43.72160065651999, (11, 4452): 45.09772024067231, (11, 4463): 49.75534446203599, (11, 4465): 49.15466294768555, (11, 4619): 58.76344968285197, (11, 4645): 58.74038350645826, (11, 4657): 59.25462727678636, (11, 4666): 59.52917444454962, (11, 4676): 60.05360494261112, (11, 4678): 59.87263112718115, (11, 4689): 60.26771603497687, (11, 4704): 63.24773273169984, (11, 4726): 84.03651268085316, (11, 4727): 83.7049661204196, (11, 4730): 83.02450475900619, (11, 4731): 83.46868815523007, (11, 4734): 82.41362742010482, (11, 4735): 82.31148232295303, (11, 4736): 82.65513197705327, (11, 4737): 82.3493881060432, (11, 4738): 82.57381863676886, (11, 4756): 83.01922651607306, (11, 4760): 80.31056121617245, (11, 4761): 80.08002096671174, (11, 4762): 80.11205065448387, (11, 4765): 80.59918586203123, (11, 4773): 84.48279809418332, (11, 4774): 84.52563741177859, (11, 4790): 84.21170065471186, (11, 4795): 83.83725850683285, (11, 4799): 84.84840805538573, (11, 4801): 86.00557392367928, (11, 4804): 83.52734171902377, (11, 4805): 83.22452235709748, (11, 4806): 84.90068882380669, (11, 4815): 84.8837136101259, (11, 4816): 85.55648549643894, (11, 4817): 86.11153693491353, (11, 4826): 85.49846117355129, (11, 4830): 85.19724754910891, (11, 4839): 81.29605288694701, (11, 4840): 81.75967284425194, (11, 4841): 81.19787503664877, (11, 4846): 80.90203166847625, (11, 4848): 81.16610766871425, (11, 4850): 81.524478936641, (11, 4871): 76.13099777711703, (11, 4883): 79.44452625158412, (11, 4900): 77.26354911578817, (11, 4901): 77.12204292112774, (11, 4917): 66.21966733212048, (11, 4931): 64.56438896539963, (11, 4944): 66.1216046786383, (11, 4956): 65.15586339488875, (11, 4958): 65.68495384643957, (11, 4959): 65.7725113317644, (11, 4961): 65.2538488654708, (11, 4966): 65.09164445469568, (11, 5207): 63.380831738603334, (11, 5272): 27.324051019905642, (11, 5283): 27.259177152022776, (11, 5287): 28.585004287537053, (11, 5289): 28.6544800677846, (11, 5293): 26.078750464785784, (11, 5295): 25.715862483184146, (11, 5296): 26.534023938625506, (11, 5298): 26.9956970314685, (11, 5303): 27.679982265069437, (11, 5305): 28.91627321668718, (11, 5306): 30.12726686172284, (11, 5307): 29.049334846985087, (11, 5308): 29.123476039482348, (11, 5313): 28.12963589784582, (11, 5314): 27.75589345785014, (11, 5317): 29.646729867809327, (11, 5319): 27.91327509271653, (11, 5324): 27.314047599678663, (11, 5326): 26.897325191155335, (11, 5348): 30.83598295852989, (11, 5351): 31.90216200377227, (11, 5399): 29.901998571885283, (11, 5413): 33.70646614967037, (11, 5422): 29.050485093036105, (11, 5445): 29.469794203899507, (11, 5448): 29.541203628271823, (11, 5456): 30.433135322643732, (11, 5467): 30.61173680048737, (11, 5624): 30.371839874010707, (11, 5671): 18.386937422177603, (11, 5672): 17.685993363947887, (11, 5797): 28.929606943659596, (11, 5871): 41.15441344504095, (11, 5976): 38.9055538821481, (11, 6118): 242.43996938987323, (11, 6248): 255.4207499738587, (11, 6345): 79.57816982416135, (11, 6352): 81.95283439940361, (11, 6354): 78.80040005668572, (11, 6359): 78.68677373339423, (11, 6376): 82.43479187939955, (11, 6378): 79.12193222168304, (11, 6381): 79.12767195840915, (11, 6383): 79.94042517753265, (11, 6396): 80.81575063584935, (11, 6399): 79.97530696958712, (11, 6408): 81.51803122303585, (11, 6409): 79.47913376121882, (11, 6419): 81.94393338043496, (11, 6422): 80.48375863042008, (11, 6423): 80.62555292890079, (11, 6424): 77.98875070138384, (11, 6439): 78.1481184840486, (11, 6464): 78.5221469221333, (11, 6465): 79.07429967066983, (11, 6469): 79.44501372405067, (11, 6470): 79.74539925408148, (11, 6472): 78.02587916900389, (11, 6480): 76.95553905269585, (11, 6486): 73.90311440678374, (11, 6497): 74.84726605344609, (11, 6503): 76.53410053596548, (11, 6508): 77.35216720739953, (11, 6509): 76.43777134058277, (11, 6521): 75.9636954065712, (11, 6544): 75.16059608322777, (11, 6552): 78.45178498099975, (11, 6553): 78.72466860402214, (11, 6554): 79.0156205050213, (11, 6578): 78.13605123445603, (11, 6582): 77.37087973245235, (11, 6601): 77.79895843188062, (11, 6609): 76.47984866014136, (11, 6610): 76.17730946933976, (11, 6611): 76.68353130809511, (11, 6614): 77.17716508746845, (11, 6615): 76.92450161244092, (11, 6616): 75.8770352830588, (11, 6617): 76.27295393210267, (11, 6618): 75.0857330978978, (11, 6619): 77.28034783396635, (11, 6620): 75.51973157211329, (11, 6621): 75.70598100944251, (11, 6622): 75.88786107709358, (11, 6623): 76.82056274874306, (11, 6624): 76.68224120598822, (11, 6625): 76.91911167407721, (11, 6626): 77.44822377552077, (11, 6627): 77.54826856806854, (11, 6628): 75.21698011946773, (11, 6629): 76.18195060864564, (11, 6630): 77.70144539939898, (11, 6632): 76.40210877370423, (11, 6634): 77.75480863575935, (11, 6635): 75.98752747644326, (11, 6636): 75.74094532150446, (11, 6637): 76.4987327042951, (11, 6638): 77.33663928435901, (11, 6639): 77.31594596968571, (11, 6640): 77.47054264132659, (11, 6641): 75.43948874138268, (11, 6642): 77.09786124385022, (11, 6643): 77.72798019970924, (11, 6645): 77.08479099549794, (11, 6646): 75.45489783960095, (11, 6647): 77.14955480735499, (11, 6653): 77.04460063328987, (11, 6655): 77.42765255289292, (11, 6658): 77.63757356812658, (11, 6662): 76.86323470299166, (11, 6819): 88.24364980123167, (11, 6996): 78.49799544266222, (11, 7059): 74.81254309840575, (11, 7187): 73.61621865688828, (11, 7304): 86.07084752018348, (11, 7528): 75.11594322915393, (11, 7720): 56.880305337333255, (11, 7793): 55.39906843199302, (11, 7807): 55.73029801353896, (11, 7808): 55.07474378552368, (11, 7831): 72.20403128306152, (11, 7850): 70.89877723839233, (11, 7852): 72.10458466985851, (11, 8012): 60.561851603719596, (11, 8125): 45.461841435973554, (11, 8208): 50.620902670895404, (11, 8392): 64.35551676754729, (11, 8651): 106.01888218355127, (11, 9088): 95.22320915806154, (11, 9443): 105.6381756084831, (11, 9444): 104.94409414830794, (11, 9828): 121.65581365714286, (11, 9868): 124.28794690827975, (11, 10180): 44.44965156450169, (11, 10256): 34.005186878748475, (11, 10276): 40.022346724721416, (11, 10378): 43.594159347040886, (11, 10676): 43.92609698320088, (11, 10714): 50.48539972554833, (11, 10730): 51.165800852341214, (11, 10862): 84.7604230804316, (11, 10881): 84.16393974725183, (11, 10883): 84.47727663397278, (11, 10885): 84.83025176391153, (11, 10891): 84.96999409566878, (11, 10909): 84.43068222031418, (11, 10911): 83.74097863049528, (11, 10913): 84.07435036186546, (11, 10915): 83.76859589881467, (11, 10919): 83.42290893767112, (11, 11037): 95.0600350481684, (11, 11039): 94.40518391071612, (11, 11516): 119.21680317726457, (11, 11856): 43.38288572872922, (11, 11857): 42.1214034887668, (11, 11861): 42.73782113710608, (11, 11881): 43.81698030644726, (11, 11902): 42.8576317459553, (11, 11911): 43.73710363700222, (11, 11914): 43.406564200629006, (11, 11922): 43.74668646538474, (11, 11924): 44.240305694107995, (11, 11926): 44.022351024831785, (11, 11950): 45.70278741590191, (11, 11963): 46.483818153633344, (11, 11983): 47.695215149015006, (11, 11985): 46.80462493332802, (11, 12009): 48.1536950028543, (11, 12010): 47.21043229965206, (11, 12018): 47.51131913903435, (11, 12020): 47.44290335206702, (11, 12021): 47.707024338149274, (11, 12024): 48.270313844528346, (11, 12025): 47.76629687543151, (11, 12027): 47.708987589254384, (11, 12031): 47.107540399669624, (11, 12032): 47.05120359501784, (11, 12035): 48.46971420486319, (11, 12041): 45.994353664975044, (11, 12045): 41.92449345414899, (11, 12145): 45.59166342434251, (11, 12275): 83.96439808159802, (11, 12294): 83.78734294610823, (11, 12358): 91.13752056340938, (11, 12463): 95.13364456332111, (11, 12465): 95.15499543842397, (11, 12482): 94.83270549651078, (11, 12503): 95.02841190556744, (11, 12506): 95.2834869005998, (11, 12549): 93.10446319475705, (11, 12559): 93.23461426176259, (11, 12569): 94.0207408433128, (11, 12572): 94.17899121128411, (11, 12574): 93.6691788235063, (11, 12576): 93.13138347717567, (11, 12591): 92.15495420440331, (11, 12608): 93.0521869451146, (11, 12696): 89.93568128325259, (11, 12710): 90.17367806560208, (11, 12728): 90.76384569889477, (11, 12766): 70.75274286878556, (11, 12771): 67.13499941521964, (11, 12790): 67.35851488214777, (11, 12795): 68.38635745575071, (11, 12797): 66.7461478517857, (11, 12798): 66.46753207950422, (11, 12811): 66.09177729676361, (11, 12830): 66.95648179486045, (11, 12848): 65.35607732921574, (11, 12850): 64.39752199428509, (11, 12852): 66.51481756724002, (11, 12854): 66.58551497052173, (11, 12859): 64.88695961672316, (11, 12861): 66.03452139239086, (11, 12865): 66.70540207943442, (11, 12866): 66.27695423481316, (11, 12867): 66.58735189110583, (11, 12874): 66.49787819569715, (11, 12875): 66.26528255971807, (11, 12881): 66.95406096370193, (11, 12883): 66.83055597428142, (11, 12885): 66.33943205933032, (11, 12888): 66.56303538933909, (11, 12889): 66.28287952681958, (11, 12892): 66.66277630880242, (11, 12893): 66.8726580910445, (11, 12896): 66.52118693344681, (11, 12906): 67.88703605441758, (11, 13018): 76.59897133258472, (11, 13071): 78.37028337761934, (11, 13131): 72.25981383821768, (11, 13146): 69.95026702814673, (11, 13159): 80.15599927585379, (11, 13193): 71.93474741125218, (11, 13198): 71.14295603089856, (11, 13292): 67.92330038771395, (11, 13296): 64.2271063807689, (11, 13406): 77.26446974336625, (11, 13407): 77.7117213305055, (11, 13417): 80.79138670191945, (11, 13418): 80.99913019887322, (11, 13438): 77.65484686857914, (11, 13442): 76.4672561467754, (11, 13443): 76.79522921730506, (11, 13764): 121.41555076507048, (11, 13766): 120.91846953025218, (11, 13771): 122.28384193511141, (11, 13783): 120.37333814482258, (11, 13784): 119.99673694449258, (11, 13792): 124.56402515301566, (11, 13824): 120.8928930914306, (11, 14017): 112.8767195658329, (11, 14870): 72.50410530717186, (11, 14997): 76.1526322372459, (11, 15000): 75.81532085826927, (11, 15003): 75.10762266919116, (11, 15006): 75.36357367217884, (11, 15007): 74.89590385888604, (11, 15056): 74.1003465857692, (11, 15063): 74.3321441643429, (11, 15069): 74.17057386435218, (11, 15076): 74.62156139688116, (11, 15086): 76.36687160072393, (11, 15087): 76.43998718263715, (11, 15111): 78.04228813972031, (11, 15116): 77.09349381234226, (11, 15722): 89.02050590039164, (11, 15998): 91.96398730229532, (11, 16073): 210.14278384305132, (11, 16939): 248.16328294484012, (11, 16940): 247.4661874030169, (11, 16951): 248.50389378713547, (11, 16963): 248.5106018004849, (11, 16965): 249.25145912413268, (11, 16969): 249.19892023518733, (11, 16970): 248.7313520886588, (11, 16971): 248.05492507341918, (11, 16973): 248.0975562094548, (11, 16974): 249.63357737044447, (11, 16976): 248.72806890749948, (11, 16978): 248.2030033161483, (11, 16980): 248.90313933661952, (11, 16982): 249.72003153489274, (11, 17045): 277.914583805253, (11, 17048): 278.8440141253275, (11, 17304): 68.14134345756648, (11, 17305): 68.70983169036641, (11, 17330): 68.74893852975809, (11, 17334): 67.3092829096919, (11, 17343): 69.43310513765528, (11, 17345): 68.243671046068, (11, 17347): 69.32511702236195, (11, 17351): 66.40852690299047, (11, 17372): 67.59747606255358, (11, 17373): 69.24877485187572, (11, 17377): 69.44270867570803, (11, 17382): 68.56852311221387, (11, 17383): 68.41097438342045, (11, 17389): 67.97351079046577, (11, 17400): 68.70658180212203, (11, 17401): 68.53844675591358, (11, 17402): 68.85005754990121, (11, 17403): 69.01446400396581, (11, 17440): 69.3379712115143, (11, 17455): 69.90765200135678, (11, 17491): 70.69502883671566, (11, 17507): 64.57992685488848, (11, 17509): 64.79463083888821, (11, 17590): 67.1925767485518, (11, 17615): 58.508475725911765, (11, 17642): 59.4426879386468, (11, 17643): 59.77503211690092, (11, 17668): 58.25735459062054, (11, 17721): 55.10604188926439, (11, 17754): 58.88426188855705, (11, 17769): 63.65146464774385, (11, 17776): 63.61595945403867, (11, 17804): 64.22471401200343, (11, 17809): 64.68134810108108, (11, 17824): 63.79352320718082, (11, 17837): 65.28575695378434, (11, 17838): 65.87429595735574, (11, 17862): 65.80830624012512, (11, 17866): 66.48494524247023, (11, 17872): 65.16590634309271, (11, 17873): 64.78432177076611, (11, 17881): 65.45505690987741, (11, 17947): 189.09162912397574, (11, 17951): 188.01753344560072, (11, 17953): 187.70756469636623, (11, 17954): 187.7140965351533, (11, 17959): 189.05068508556457, (11, 17963): 188.8544237595881, (11, 18000): 183.10547171410317, (11, 18001): 183.17937471572057, (11, 18111): 194.70663639571654, (11, 18148): 164.81058356219384, (11, 18166): 175.775581117915, (11, 18189): 187.19963378992242, (11, 18239): 69.11693598454129, (11, 18240): 69.21562559366905, (11, 18245): 69.21264256007531, (11, 18247): 69.22549438587961, (11, 18251): 69.33755466410807, (11, 18256): 69.58026676986371, (11, 18258): 69.52807578445464, (11, 18259): 69.6043879664412, (11, 18260): 69.72640626510314, (11, 18262): 69.88165703864529, (11, 18263): 69.66899337879069, (11, 18264): 69.78367241229284, (11, 18266): 70.00762506837789, (11, 18267): 70.10515055688019, (11, 18268): 70.19199217300867, (11, 18269): 70.3974164027834, (11, 18275): 70.30097291740388, (11, 18285): 69.70364636009882, (11, 18308): 67.54717484612907, (11, 18313): 67.10962320664403, (11, 18314): 67.63495031789982, (11, 18315): 70.09921853806378, (11, 18316): 70.22494937723029, (11, 18317): 70.32981142799962, (11, 18320): 70.22684575844622, (11, 18321): 70.34732111113657, (11, 18322): 70.48421093976657, (11, 18324): 70.3973112396754, (11, 18325): 70.63010839707826, (11, 18326): 70.53695360879851, (11, 18327): 70.5423360975903, (11, 18329): 70.57988565537124, (11, 18330): 70.89522564405091, (11, 18331): 70.67127398157227, (11, 18332): 70.51247140940957, (11, 18333): 70.74741488138325, (11, 18336): 70.40904114283074, (11, 18337): 70.39953386822556, (11, 18403): 71.06326018834618, (11, 18432): 72.07621500287419, (11, 18451): 71.38779430304898, (11, 18466): 70.43497524112145, (11, 18481): 69.79095492834398, (11, 18483): 69.88929279357686, (11, 18484): 69.6856189078096, (11, 18485): 68.97186353394474, (11, 18486): 68.96376938654923, (11, 18487): 68.54459484877839, (11, 18489): 69.26287426985745, (11, 18490): 69.29342753765324, (11, 18491): 69.43426379968092, (11, 18492): 68.32750312424831, (11, 18493): 68.79568687124113, (11, 18494): 69.285919408175, (11, 18495): 69.17372555262249, (11, 18496): 69.10742441414048, (11, 18497): 68.35629897260918, (11, 18498): 68.82871982127637, (11, 18499): 69.08473648681853, (11, 18501): 68.72417904840907, (11, 18502): 68.54885794886744, (11, 18503): 68.53538344030063, (11, 18504): 69.28764146472113, (11, 18506): 68.46355146645884, (11, 18507): 68.23965762829661, (11, 18508): 68.95290275256566, (11, 18509): 68.8621341528144, (11, 18510): 68.40062909485849, (11, 18511): 68.6429563177015, (11, 18512): 68.63828083365142, (11, 18515): 69.16248830109375, (11, 18516): 68.84983629771857, (11, 18517): 68.48616462596021, (11, 18518): 69.0712797382068, (11, 18519): 69.37985620904395, (11, 18520): 69.02328450449934, (11, 18522): 70.25530542800225, (11, 18523): 70.1804330070953, (11, 18532): 70.24107476507369, (11, 18535): 70.00485832499497, (11, 18537): 69.87406129351936, (11, 18539): 69.84488952714077, (11, 18540): 69.80041165740161, (11, 18541): 69.81561498929825, (11, 18542): 69.83566170366386, (11, 18543): 69.69256945668467, (11, 18546): 69.57674300521184, (11, 18555): 69.773164907188, (11, 18556): 69.73564055191304, (11, 18565): 70.08066722940656, (11, 18567): 69.92714488000342, (11, 18568): 69.90965341766662, (11, 18577): 70.73845464366349, (11, 18583): 70.8921210446827, (11, 18605): 71.42054330504273, (11, 18608): 69.56746022587349, (11, 18616): 72.18524713443401, (11, 18618): 72.66558713484707, (11, 18625): 73.2062714886643, (11, 18645): 72.93868215238852, (11, 18646): 72.8346561967788, (11, 18653): 71.5405693891645, (11, 18654): 72.04179016719384, (11, 18655): 71.55172091214816, (11, 18666): 75.03811824158663, (11, 18837): 84.24683218288638, (11, 18974): 73.92423493205283, (11, 18999): 75.79361673305286, (11, 19000): 76.00696135172569, (11, 19174): 75.31312237129906, (11, 19342): 80.91613006005785, (11, 19455): 70.54726931212903, (11, 19555): 68.96904079166472, (11, 19564): 72.93324103295438, (11, 19573): 71.95933668013886, (11, 19586): 71.28452287499242, (11, 19605): 70.75443271848927, (11, 19611): 71.27084693225441, (11, 19614): 70.02007859156559, (11, 19641): 74.55165583229049, (11, 19702): 75.6088447228126, (11, 19713): 75.01553016195051, (11, 19731): 62.808627667211034, (11, 19819): 71.64845318097113, (11, 19893): 12.5, (11, 19899): 12.5, (11, 19929): 12.5, (11, 19951): 12.5, (11, 19962): 12.5, (11, 19970): 12.5, (11, 19971): 12.5, (11, 19972): 12.5, (11, 19975): 12.5, (11, 19978): 15.365780066546797, (11, 19987): 15.763055445877114, (11, 19989): 14.63315228359032, (11, 20039): 16.15473423111005, (11, 20043): 17.137863609383356, (11, 20047): 17.131430671186973, (11, 20052): 15.546617926263687, (11, 20054): 15.38129839326291, (11, 20085): 25.045330548068616, (11, 20104): 25.633373383133307, (11, 20132): 21.754281013282437, (11, 20203): 12.5, (11, 20280): 12.5, (11, 20285): 12.5, (11, 20290): 12.5, (11, 20297): 12.5, (11, 20309): 13.417655030927387, (11, 20453): 25.20401465718332, (11, 20485): 12.5, (11, 20520): 12.5, (11, 20526): 12.5, (11, 20698): 149.7891341932574, (11, 20868): 169.65261419031285, (11, 21042): 46.350800878191144, (11, 21057): 45.561172601272126, (11, 21066): 44.93428043766306, (11, 21075): 46.45981469169325, (11, 21093): 44.98192676077169, (11, 21098): 42.3818748034254, (11, 21127): 45.5771997728516, (11, 21130): 44.74531565208229, (11, 21144): 46.00326809986415, (11, 21146): 45.6552560075097, (11, 21147): 46.38867375660515, (11, 21148): 45.79091767939436, (11, 21153): 51.00184684627411, (11, 21293): 43.44362529384491, (11, 21426): 56.08810930072323, (11, 21442): 58.62450954533827, (11, 21451): 58.83923374953358, (11, 21466): 56.60798198332798, (11, 21469): 56.36566517957768, (11, 21471): 56.76162576449072, (11, 21473): 56.40317858158553, (11, 21475): 56.55377862865428, (11, 21482): 56.73120276154183, (11, 21484): 56.50866853559598, (11, 21488): 56.78665532545407, (11, 21494): 55.845118639023745, (11, 21498): 55.840427189074326, (11, 21500): 55.29062002799558, (11, 21514): 52.45691412753096, (11, 21537): 53.73406387671533, (11, 21662): 50.50155359137752, (11, 21691): 50.92880624625826, (11, 21757): 57.24547722252815, (11, 21777): 45.97806187012946, (11, 21778): 46.42910408805888, (11, 21779): 45.67000274322513, (11, 21790): 46.04273081673414, (11, 21802): 45.051394700800834, (11, 21824): 44.07988050668122, (11, 21874): 44.93463628757354, (11, 21879): 44.30678650449709, (11, 21983): 47.771426502957596, (11, 22002): 40.10872294943512, (11, 22132): 56.04350260004582, (11, 22261): 123.4643145669244, (11, 22298): 121.66505389743992, (11, 22339): 129.51694241444585, (11, 22508): 109.30454684668908, (11, 22841): 297.77057829989093, (11, 22842): 297.7379722226805, (11, 22874): 295.81567773373155, (11, 22941): 296.1238496545271, (11, 22956): 297.1903620281342, (11, 22960): 297.60116675089347, (11, 22968): 298.1766129108789, (11, 22970): 298.552437880835, (11, 22974): 298.7628819246306, (11, 22980): 300.0771494213648, (11, 23025): 299.44983315008204, (11, 23028): 299.051599769377, (11, 23081): 300.61627655574375, (11, 23104): 297.3154048060494, (11, 23147): 287.23108925614355, (11, 23298): 48.85959354077479, (11, 23376): 48.31596035902917, (11, 23381): 44.824726988981645, (11, 23529): 46.62284202753914, (11, 23556): 46.67666594865898, (11, 23718): 51.179074649703615, (11, 24001): 54.434680251507366, (11, 24094): 51.32513252020071, (11, 24129): 52.557003122057644, (11, 24174): 48.00414777676181, (11, 24235): 49.39350946764925, (11, 24259): 51.9658010013958, (11, 24260): 51.67157780202622, (11, 24261): 51.573757263510785, (11, 24305): 54.063489264035, (11, 24306): 54.073959483371794, (11, 24307): 53.81871231355079, (11, 24308): 60.602596047903525, (11, 24498): 61.45057314190087, (11, 24499): 61.39239876638866, (11, 24500): 61.222854325109445, (11, 24668): 64.35497416189746, (11, 24711): 61.262753080556585, (11, 24756): 60.68393741393638, (11, 24788): 61.79057680893722, (11, 24809): 58.49744143432623, (11, 24813): 59.6584811179738, (11, 24821): 59.338088635630285, (11, 24825): 59.31241244545187, (11, 24832): 58.4853967271939, (11, 24833): 58.83550020224167, (11, 24835): 59.10523522955396, (11, 24837): 59.85091513108861, (11, 24840): 58.334789638116526, (11, 24841): 59.07527815699425, (11, 24844): 58.22018545969418, (11, 24845): 59.04877511601392, (11, 24846): 58.30199404182507, (11, 24849): 58.43123603422016, (11, 24850): 59.60711153676084, (11, 24863): 55.759904018468134, (11, 24866): 56.416922376262136, (11, 24885): 56.69515973828385, (11, 24886): 56.45948565402165, (11, 24889): 58.84651520291214, (11, 24903): 59.823102967533025, (11, 24909): 58.28817168738912, (11, 24999): 89.09601041619136, (11, 25019): 89.27954405479761, (11, 25028): 88.49084506791112, (11, 25137): 12.5, (11, 25145): 12.5, (11, 25208): 20.256512311956225, (11, 25233): 20.032950527457118, (11, 25371): 12.5, (11, 25377): 12.5, (11, 25828): 43.00731401056836, (11, 25851): 49.31262032262472, (11, 25874): 43.22514124510559, (11, 25898): 40.67140366633061, (11, 25946): 43.64589590558098, (11, 26047): 31.69332476095142, (11, 26066): 17.418029920286262, (11, 26197): 24.80259276840969, (11, 26212): 65.4179002288337, (11, 26253): 67.73521802100305, (11, 26254): 66.81056937595355, (11, 26257): 66.1313496372201, (11, 26258): 67.30797228492062, (11, 26260): 66.6928073511174, (11, 26266): 67.29635753818513, (11, 26267): 66.60990667298944, (11, 26271): 66.6168849590089, (11, 26304): 58.49518397084566, (11, 26305): 58.528813209673814, (11, 26363): 45.60051379425839, (11, 26441): 120.77934189529566, (11, 26442): 120.6483492541645, (11, 26450): 119.45045645100535, (11, 26459): 118.89724066213607, (11, 26462): 118.86284661232366, (11, 26467): 122.30535399442593, (11, 26471): 121.5681756120956, (11, 26472): 121.53307324621066, (11, 26473): 121.5584479940111, (11, 26476): 121.6852301136906, (11, 26485): 119.70888790750939, (11, 26493): 119.98173235578105, (11, 26524): 119.17696940429947, (11, 26525): 119.16565782302295, (11, 26556): 121.08086415551868, (11, 26560): 120.59010226927425, (11, 26561): 119.75824039540552, (11, 26564): 120.86699393447122, (11, 26569): 119.70117869237089, (11, 26570): 119.5492675511642, (11, 26573): 119.94238758695471, (11, 26581): 120.09835871947584, (11, 26583): 119.72790023324869, (11, 26593): 120.33965670587395, (11, 26837): 122.72244103954328, (11, 26844): 123.42491855897276, (11, 26863): 122.3441975969435, (11, 26893): 124.54208952914543, (11, 26902): 125.51067542641205, (11, 26905): 124.13384636746054, (11, 26912): 125.01642705150714, (11, 26921): 123.36886475960192, (11, 26922): 122.08686352547348, (11, 27212): 119.93396049316323, (11, 27218): 118.70087286888531, (11, 27239): 121.4918159266331, (11, 27257): 120.8175987899456, (11, 27274): 121.8537983099202, (11, 27279): 121.80107196439727, (11, 27282): 120.91453514028763, (11, 27283): 121.0440358084291, (11, 27285): 122.32327240647405, (11, 27286): 121.7095492655346, (11, 27290): 120.17592086868201, (11, 27295): 119.45909979654387, (11, 27300): 121.96227620817281, (11, 27344): 120.10848039037813, (11, 27366): 121.22348969368873, (11, 27383): 122.63891535433618, (11, 27398): 123.44480499342616, (11, 27406): 122.47996213854005, (11, 27407): 122.65243914694832, (11, 27426): 120.7392364584861, (11, 27432): 117.12271675338276, (11, 27460): 119.284764311149, (11, 27523): 123.40432313820823, (11, 27545): 137.05071423000413, (11, 27602): 158.19192848898763, (11, 27606): 158.44367292989577, (11, 27646): 139.16357032028404, (11, 27667): 143.295678647498, (11, 27672): 143.42437306070104, (11, 27674): 142.7741897206084, (11, 27688): 143.0187700542467, (11, 27692): 144.24058825908298, (11, 27693): 143.63989847362419, (11, 27705): 143.70800470264194, (11, 27712): 144.08831250040208, (11, 27786): 156.0833560198415, (11, 27790): 152.74234979206696, (11, 27791): 152.40332173280183, (11, 27795): 155.00147201048944, (11, 27801): 152.59704141152235, (11, 27813): 156.84101530833132, (11, 27816): 155.88007234854265, (11, 27823): 152.49717905325346, (11, 27830): 154.72845957438304, (11, 27884): 133.37030572198154, (11, 27885): 137.5910026598707, (11, 27896): 134.9752263756795, (11, 27919): 134.69523733092535, (11, 27922): 135.37159279266757, (11, 27930): 133.8747780477602, (11, 27934): 134.12792331332338, (11, 27935): 134.3522810165121, (11, 27948): 160.39802749686567, (11, 27951): 160.06457202343023, (11, 28061): 153.994807018874, (11, 28290): 192.70376405595525, (11, 28292): 193.9067106655368, (11, 28293): 192.96705607757988, (11, 28295): 192.84538213911375, (11, 28296): 192.78448020376902, (11, 28297): 192.08997567452096, (11, 28302): 192.0006682634583, (11, 28310): 223.8483233774795, (11, 28313): 224.90650608687585, (11, 28372): 224.2632308942213, (11, 28398): 224.38919557425723, (11, 28399): 224.1582431466944, (11, 28400): 224.63282878620458, (11, 28401): 223.29077114565868, (11, 28445): 224.71828665837518, (11, 28475): 221.79536592348478, (11, 28885): 41.5795987333732, (11, 28886): 41.01221673152568, (11, 28915): 39.91573776067324, (11, 28916): 40.12602103691389, (11, 28917): 39.710727130944214, (11, 28921): 42.31842266160813, (11, 28931): 41.906063314927145, (11, 28945): 36.28657958955395, (11, 28982): 38.04392652034158, (11, 29219): 32.69490693774588, (11, 29228): 31.787459457618635, (11, 29246): 36.13732965811186, (11, 29248): 35.076627480571965, (11, 29282): 33.59545516261648, (11, 29290): 37.95702878995516, (11, 29291): 37.35207066982022, (11, 29292): 37.78070078173385, (11, 29293): 37.16262825330263, (11, 29294): 37.24783757261727, (11, 29298): 36.95176152879037, (11, 29299): 36.63956909211821, (11, 29304): 36.65158461811959, (11, 29317): 35.63458301698767, (11, 29323): 35.5934358741215, (11, 29330): 36.01313579028576, (11, 29331): 36.46379334852638, (11, 29344): 30.356751838798775, (11, 29445): 18.475996965266773, (11, 29724): 295.7154715202449, (11, 29738): 296.0646786912965, (11, 29745): 295.07878252899275, (11, 29748): 295.44463184738777, (11, 29750): 296.08397074771455, (11, 29759): 294.9455762904619, (11, 29772): 296.23961900153427, (11, 29781): 295.9617921632914, (11, 29784): 295.6698801239109, (11, 29790): 296.2722208365354, (11, 29811): 295.60725974786834, (11, 29817): 298.40769862679343, (11, 29818): 298.139269084974, (11, 29929): 294.8521110907804, (11, 30039): 298.9119195113899, (11, 30066): 295.6745084330295, (11, 30116): 284.1964653859468, (11, 30238): 267.0924953724379, (11, 30248): 275.0062588719726, (11, 30260): 275.15040080304294, (11, 30545): 43.33069827113045, (11, 30733): 43.70162178584901, (11, 30756): 36.81356828271827, (11, 30921): 38.67346343713215, (11, 31079): 90.19003849799739, (11, 31149): 85.67229903120523, (11, 31154): 86.53383623840946, (11, 31160): 85.60424215484937, (11, 31163): 86.62157006150747, (11, 31189): 87.53495317773854, (11, 31215): 88.22005429505398, (11, 31259): 92.2982168951713, (11, 31262): 92.21540883060538, (11, 31430): 92.76957948367848, (11, 31568): 105.23796110222258, (11, 31751): 93.0794654385148, (13, 109): 74.1792052491195, (13, 872): 187.76739338327957, (13, 873): 188.6271581975448, (13, 877): 188.25138593624055, (13, 879): 188.37382043512113, (13, 884): 187.39121693220636, (13, 889): 187.95556763555092, (13, 891): 187.12066065841805, (13, 892): 189.0516459739474, (13, 894): 188.96470076760494, (13, 896): 188.22484959610898, (13, 903): 188.22326567485612, (13, 909): 186.93473223026206, (13, 910): 187.32906807008794, (13, 912): 186.7490521745008, (13, 913): 186.09141294353205, (13, 916): 185.88727731755284, (13, 926): 187.67723281718636, (13, 927): 187.40018498113957, (13, 948): 186.81735733146542, (13, 961): 187.52861432962115, (13, 962): 187.6611608371915, (13, 963): 187.79890108096012, (13, 967): 188.6084897222642, (13, 974): 188.0240946466885, (13, 998): 188.9058084913333, (13, 1014): 208.36821171256477, (13, 1086): 187.19638222208786, (13, 1087): 187.2875177480598, (13, 1089): 186.3932329648259, (13, 1090): 186.73772643391155, (13, 1092): 187.97151826578025, (13, 1097): 186.99122906679344, (13, 1107): 188.711182832261, (13, 1387): 69.57675696280977, (13, 1554): 58.36643472458104, (13, 1827): 226.35687482170823, (13, 1828): 226.4696378659986, (13, 1829): 226.5902121194869, (13, 1830): 226.35860205360427, (13, 1831): 226.45357402911696, (13, 1832): 226.3684004908686, (13, 1833): 226.3949231278545, (13, 1836): 226.31210734755618, (13, 1841): 226.84902497850774, (13, 1843): 226.61422092067755, (13, 1844): 226.70296301617947, (13, 1845): 226.40950734542844, (13, 1847): 225.55151412834232, (13, 1848): 225.8572637023027, (13, 1849): 227.27510008042782, (13, 1850): 227.43991130914168, (13, 1851): 226.04889025177826, (13, 1852): 226.03484522084338, (13, 1854): 226.21026983610992, (13, 1856): 225.45920338270588, (13, 1857): 225.8162467561336, (13, 1858): 227.16102215621723, (13, 1861): 226.53905045811342, (13, 1866): 225.407909159927, (13, 1867): 226.89624117090509, (13, 1868): 226.73795150376338, (13, 1870): 226.62998815080942, (13, 1871): 226.88471824634618, (13, 1875): 226.21944053909752, (13, 1880): 225.68431661148253, (13, 1882): 225.7226430068639, (13, 1883): 227.49348138962463, (13, 1889): 225.90695024356748, (13, 1893): 226.6676691826598, (13, 1894): 226.45897518372547, (13, 1899): 225.7389811660912, (13, 1900): 225.9132722331863, (13, 1902): 227.04819492287652, (13, 1905): 227.30688845814623, (13, 1907): 226.1052732281637, (13, 1910): 226.2553570093364, (13, 1917): 228.02352962642988, (13, 1920): 226.15910541415008, (13, 1935): 227.4168406946656, (13, 1937): 227.64572179419926, (13, 1946): 225.33599210084196, (13, 1949): 225.6259110456699, (13, 1950): 224.58042193921025, (13, 1951): 225.06438523154674, (13, 1952): 225.3131115449463, (13, 1953): 225.55048864416528, (13, 1954): 225.2695003524181, (13, 1958): 225.5086866463791, (13, 1960): 225.94563112018662, (13, 1968): 226.11833976423623, (13, 1969): 227.54430775495058, (13, 1974): 227.16490325405698, (13, 1975): 227.13735288045, (13, 1979): 226.52666563309594, (13, 1980): 226.4038081453398, (13, 1981): 226.64078918428322, (13, 1985): 226.81898900146484, (13, 1994): 224.04677508527828, (13, 2011): 225.68731803584552, (13, 2019): 227.88672951442877, (13, 2020): 227.59512744106706, (13, 2029): 226.42221721396007, (13, 2030): 227.39411552131153, (13, 2032): 226.196369394613, (13, 2033): 226.85272650496583, (13, 2034): 226.8087031330763, (13, 2036): 225.51020116884317, (13, 2037): 225.8476523413106, (13, 2038): 226.10353150196505, (13, 2042): 229.57213657640972, (13, 2050): 226.74527873171212, (13, 2051): 226.65907980781654, (13, 2053): 226.76698195307168, (13, 2054): 227.07256508486847, (13, 2066): 226.44436059833305, (13, 2067): 226.4648970557959, (13, 2071): 223.486556760802, (13, 2072): 224.09029406501534, (13, 2073): 222.6028015385097, (13, 2074): 222.50107313201755, (13, 2080): 221.46755663677553, (13, 2082): 224.40766353923811, (13, 2083): 224.7220703731588, (13, 2089): 224.11314764175, (13, 2090): 224.41266280051227, (13, 2092): 224.05207493638127, (13, 2098): 221.8878372931426, (13, 2099): 222.20311149718097, (13, 2101): 221.7951453141795, (13, 2102): 223.41591365856706, (13, 2103): 222.89339540270242, (13, 2104): 222.5926882991589, (13, 2106): 224.910381248127, (13, 2112): 221.98110245362176, (13, 2113): 223.6271375725338, (13, 2114): 223.9633086567445, (13, 2117): 225.12586176499278, (13, 2123): 224.08691265088632, (13, 2124): 224.420904070766, (13, 2134): 223.37795869668892, (13, 2138): 224.39711780673903, (13, 2141): 223.52169844495916, (13, 2148): 223.66313508851943, (13, 2150): 222.69195070009147, (13, 2151): 223.01761119115005, (13, 2152): 222.4832901669823, (13, 2153): 223.80850018820487, (13, 2154): 222.44611382955097, (13, 2155): 222.22885884208847, (13, 2156): 222.01282283221718, (13, 2157): 222.15446885822385, (13, 2160): 224.69557542856933, (13, 2161): 222.39081187395217, (13, 2162): 223.73769211353562, (13, 2163): 223.2798300953141, (13, 2164): 223.22786017536203, (13, 2168): 222.64767791685807, (13, 2172): 222.80199230013105, (13, 2174): 222.93308317815047, (13, 2178): 223.0302957784033, (13, 2179): 222.80141683367944, (13, 2183): 224.3335939557093, (13, 2185): 224.3329688167992, (13, 2186): 224.0778582649263, (13, 2190): 224.79897761598212, (13, 2192): 224.33201140693438, (13, 2193): 224.4393577139069, (13, 2194): 223.96241531266557, (13, 2195): 223.8469080271855, (13, 2197): 224.41175749453637, (13, 2205): 223.67918009968926, (13, 2207): 222.74043997486848, (13, 2208): 223.25636354739262, (13, 2212): 224.68110921249468, (13, 2214): 214.22338401220367, (13, 2225): 215.25285170223762, (13, 2231): 213.97347809840127, (13, 2278): 219.7699655636829, (13, 2284): 220.69257338834726, (13, 2285): 220.5257453007619, (13, 2291): 218.36926042793544, (13, 2292): 218.8092435149624, (13, 2307): 220.04202126661986, (13, 2313): 218.0668908384921, (13, 2317): 218.16957510593656, (13, 2319): 219.1280201486033, (13, 2321): 219.5458978597385, (13, 2323): 219.54993627213835, (13, 2326): 221.40374025896705, (13, 2327): 220.9748950694479, (13, 2329): 220.67548148348206, (13, 2330): 220.31905150121554, (13, 2332): 220.99519678186496, (13, 2344): 219.99526655615912, (13, 2346): 219.9295873871948, (13, 2361): 220.15187066486948, (13, 2368): 224.92661024423805, (13, 2374): 225.3633173520379, (13, 2375): 225.54386167292037, (13, 2377): 223.93149972104248, (13, 2378): 225.82141103262018, (13, 2379): 225.81727589746973, (13, 2380): 226.0120809009411, (13, 2383): 224.39841501887247, (13, 2385): 224.66848116089707, (13, 2395): 224.73794128825753, (13, 2397): 225.60115931707813, (13, 2398): 223.41288978258257, (13, 2399): 224.02516832774174, (13, 2400): 223.89364887751532, (13, 2402): 224.7029187925506, (13, 2403): 225.06680511160803, (13, 2404): 225.17931416495367, (13, 2405): 224.28552757205293, (13, 2407): 225.04091375906773, (13, 2408): 225.44844106971698, (13, 2409): 224.56381661379822, (13, 2411): 224.9882014673585, (13, 2412): 224.9211038563408, (13, 2413): 225.20933995717337, (13, 2414): 224.7134650406438, (13, 2422): 224.85093121741585, (13, 2424): 225.04054020474803, (13, 2426): 225.1349075984555, (13, 2433): 224.42595333823644, (13, 2436): 224.1953696452688, (13, 2437): 222.08132471515992, (13, 2440): 222.56082387601558, (13, 2445): 231.59300533858752, (13, 2447): 230.47198267663325, (13, 2454): 231.56704091675698, (13, 2455): 231.66280722768266, (13, 2460): 228.21636950680596, (13, 2461): 228.63398752073013, (13, 2471): 235.2356521223857, (13, 2492): 226.7514106654204, (13, 2511): 223.52145478482097, (13, 2523): 225.16728523431559, (13, 2525): 224.58380088390206, (13, 2535): 226.14794031604234, (13, 2537): 225.36915548804242, (13, 2538): 225.9412099988768, (13, 2539): 225.54958213442035, (13, 2540): 226.49689208608766, (13, 2542): 227.0012189939941, (13, 2559): 238.18459040395678, (13, 2575): 237.00103205828597, (13, 2599): 221.12058056691728, (13, 2600): 224.65972850851287, (13, 2607): 222.75808235194273, (13, 2627): 225.08774320411757, (13, 2647): 227.0021779884702, (13, 2674): 226.1277596106929, (13, 2681): 225.7688700415495, (13, 2683): 226.7875697649894, (13, 2686): 225.69690906243963, (13, 2689): 238.75162296033122, (13, 2690): 238.79752612008696, (13, 2713): 240.84282195901764, (13, 2714): 241.0023355072299, (13, 2715): 241.32951609181399, (13, 2739): 241.05745162339468, (13, 2740): 239.17023483039083, (13, 2741): 239.34569662174943, (13, 2749): 240.54138537571, (13, 2750): 240.66516680848318, (13, 2752): 240.9082515032522, (13, 2755): 241.1532694250522, (13, 2758): 241.05971312180878, (13, 2759): 241.07048257442992, (13, 2769): 240.7151363555812, (13, 2771): 239.65141957149723, (13, 2779): 239.5924256811333, (13, 2784): 235.8455064887255, (13, 2800): 236.3549732811947, (13, 2802): 238.4497774168917, (13, 2803): 238.34577683111073, (13, 2804): 238.1355427305105, (13, 2805): 238.66448756330053, (13, 2807): 238.66425170151135, (13, 2809): 238.49779980686813, (13, 2812): 236.45206758104223, (13, 2814): 238.2580718764748, (13, 2817): 238.16361504018596, (13, 2819): 238.75669740505708, (13, 2823): 236.48472579828314, (13, 2832): 239.04216367888483, (13, 2836): 237.57352260564895, (13, 2839): 238.68010801548073, (13, 2841): 238.31949612046986, (13, 2843): 238.24023155707832, (13, 2846): 237.78376036214922, (13, 2849): 239.23791751974878, (13, 2852): 238.9169898537059, (13, 2853): 239.3844490378812, (13, 2876): 239.44270526467528, (13, 2877): 240.6082905107572, (13, 2885): 240.7900196411968, (13, 2918): 239.0559236638433, (13, 2921): 239.53741538209636, (13, 2925): 237.3486795536966, (13, 2926): 236.66068657031013, (13, 2930): 238.10968613458888, (13, 2931): 237.50811601237785, (13, 2938): 239.02614841695865, (13, 2940): 240.6691618970204, (13, 2947): 238.98797987611445, (13, 2949): 238.1763052444329, (13, 2950): 238.36828559083028, (13, 2952): 238.11738855781624, (13, 2958): 238.08329949332563, (13, 2959): 238.36548344193676, (13, 2960): 238.90808009782683, (13, 2961): 238.6245722662948, (13, 2963): 237.85108876991873, (13, 2968): 237.98913047139405, (13, 2976): 237.80615330100554, (13, 2981): 232.79968884560216, (13, 2982): 232.62289350022073, (13, 2984): 232.3660004166117, (13, 3003): 231.88752022498676, (13, 3046): 229.11506777966136, (13, 3050): 231.43220805183873, (13, 3051): 231.64391380065592, (13, 3053): 231.0797994157863, (13, 3069): 234.06883113200388, (13, 3071): 231.04322441853637, (13, 3080): 240.73786596202712, (13, 3199): 230.85343050488973, (13, 3200): 230.25103878613385, (13, 3205): 233.83947332108673, (13, 3209): 230.5496798393954, (13, 3215): 230.30576376347318, (13, 3217): 229.58771913778546, (13, 3249): 230.39110355778314, (13, 3263): 235.821732572017, (13, 3289): 232.15828994060485, (13, 3301): 232.28073981648393, (13, 3302): 232.04028032139436, (13, 3307): 231.72315954107322, (13, 3310): 232.5897915785642, (13, 3391): 232.47872978851572, (13, 3509): 118.3109917799973, (13, 3510): 117.80640461967242, (13, 3511): 118.18954545136039, (13, 3512): 117.91917916521916, (13, 3514): 118.06320019676356, (13, 3519): 119.2733172087149, (13, 3536): 119.28401838171841, (13, 3545): 120.12368387163225, (13, 3548): 119.41304981013391, (13, 3572): 119.51345213788781, (13, 3581): 118.74849641595705, (13, 3583): 118.59532605399723, (13, 3601): 120.15521542891892, (13, 3656): 119.17279946808088, (13, 3669): 117.85742906298589, (13, 3670): 118.29881866223224, (13, 3695): 115.83589630925202, (13, 3696): 116.2003019107163, (13, 3782): 120.50359369669607, (13, 3792): 119.80404242925896, (13, 3989): 98.0915057507865, (13, 4008): 100.70767145760105, (13, 4031): 100.27453517447641, (13, 4045): 99.59516507713991, (13, 4144): 100.00460846477357, (13, 4145): 97.71681623685005, (13, 4164): 99.0711109623279, (13, 4168): 98.40975560265456, (13, 4173): 98.32103394237437, (13, 4181): 96.74505440186317, (13, 4228): 94.90444616932034, (13, 4248): 94.74719506554584, (13, 4254): 83.12309215971125, (13, 4260): 82.9154964096543, (13, 4262): 83.92648918590957, (13, 4273): 83.58067993022932, (13, 4319): 77.25591865632549, (13, 4326): 76.93840259961644, (13, 4328): 76.95046697467312, (13, 4334): 77.65705682043608, (13, 4335): 77.53579848175674, (13, 4372): 113.14595467162376, (13, 4413): 122.30719084329384, (13, 4434): 112.45495003034198, (13, 4447): 112.39827610154778, (13, 4452): 112.7385010456105, (13, 4463): 104.89828568718698, (13, 4465): 104.9029924599602, (13, 4619): 126.58394578550276, (13, 4645): 127.46510055567252, (13, 4657): 127.66247558531241, (13, 4666): 127.49396177094773, (13, 4676): 128.46173833986754, (13, 4678): 128.48062705686007, (13, 4689): 128.3168936431398, (13, 4704): 133.25400935041876, (13, 4726): 153.74503179211962, (13, 4727): 153.4044211945414, (13, 4730): 152.71861923138295, (13, 4731): 153.08118179083735, (13, 4734): 152.50803984650838, (13, 4735): 152.32725435234545, (13, 4736): 152.61354732837646, (13, 4737): 152.2088737202356, (13, 4738): 152.38528708232027, (13, 4756): 152.80182662588624, (13, 4760): 150.3966142649779, (13, 4761): 150.31095109280588, (13, 4762): 150.1000059504834, (13, 4765): 150.64777249623626, (13, 4773): 154.27755309516837, (13, 4774): 154.19682806643732, (13, 4790): 154.01796312676007, (13, 4795): 153.6648006077101, (13, 4799): 154.46210751422393, (13, 4801): 155.47983323824147, (13, 4804): 153.50200015544223, (13, 4805): 153.21509705432686, (13, 4806): 154.39686272750674, (13, 4815): 154.26768015357112, (13, 4816): 155.0178559815039, (13, 4817): 155.44351278841359, (13, 4826): 154.85722283229896, (13, 4830): 154.48421540142508, (13, 4839): 151.40149867560834, (13, 4840): 151.81578887001936, (13, 4841): 151.18842294855705, (13, 4846): 150.9088728855506, (13, 4848): 151.05459302151678, (13, 4850): 151.40180146689454, (13, 4871): 146.4310940944067, (13, 4883): 149.6888757689434, (13, 4900): 147.7007062203255, (13, 4901): 147.45483988142993, (13, 4917): 131.11929166446842, (13, 4931): 128.96730484600653, (13, 4944): 131.18636922242968, (13, 4956): 129.53971163370957, (13, 4958): 129.83078156032602, (13, 4959): 129.6663902817339, (13, 4961): 129.83107102093413, (13, 4966): 129.2198057752651, (13, 5207): 126.8841295996491, (13, 5272): 73.39744232379766, (13, 5283): 74.31962626891512, (13, 5287): 76.77655009076135, (13, 5289): 77.2158895844422, (13, 5293): 72.59575094231225, (13, 5295): 75.04880159094284, (13, 5296): 75.62512303619484, (13, 5298): 75.92881512461717, (13, 5303): 77.15981528911826, (13, 5305): 74.08320871253281, (13, 5306): 74.29058914899127, (13, 5307): 73.68555908216024, (13, 5308): 74.68346186939803, (13, 5313): 73.87088268561065, (13, 5314): 74.19003427892433, (13, 5317): 75.09230752642047, (13, 5319): 76.46689884519263, (13, 5324): 75.51541432103846, (13, 5326): 74.8677200373542, (13, 5348): 74.63021632488271, (13, 5351): 76.14703217190726, (13, 5399): 78.5895911319494, (13, 5413): 78.6303770586586, (13, 5422): 78.45499613208298, (13, 5445): 76.75822304676839, (13, 5448): 75.95109979247209, (13, 5456): 76.41539186066376, (13, 5467): 77.33598774239023, (13, 5624): 66.36360990252055, (13, 5671): 85.71370991288603, (13, 5672): 84.4801775386079, (13, 5797): 99.96720636848299, (13, 5871): 95.48842343946701, (13, 5976): 86.49398779224646, (13, 6118): 178.10098330039062, (13, 6248): 189.0509223733002, (13, 6345): 12.5, (13, 6352): 12.5, (13, 6354): 12.5, (13, 6359): 12.5, (13, 6376): 12.5, (13, 6378): 12.5, (13, 6381): 12.5, (13, 6383): 12.5, (13, 6396): 12.5, (13, 6399): 12.5, (13, 6408): 12.5, (13, 6409): 12.5, (13, 6419): 12.5, (13, 6422): 12.5, (13, 6423): 12.5, (13, 6424): 12.5, (13, 6439): 12.5, (13, 6464): 12.5, (13, 6465): 12.5, (13, 6469): 12.5, (13, 6470): 12.5, (13, 6472): 12.5, (13, 6480): 12.5, (13, 6486): 12.5, (13, 6497): 12.5, (13, 6503): 12.5, (13, 6508): 12.5, (13, 6509): 12.5, (13, 6521): 12.5, (13, 6544): 12.5, (13, 6552): 12.5, (13, 6553): 12.5, (13, 6554): 12.5, (13, 6578): 12.5, (13, 6582): 12.5, (13, 6601): 12.5, (13, 6609): 12.5, (13, 6610): 12.5, (13, 6611): 12.5, (13, 6614): 12.5, (13, 6615): 12.5, (13, 6616): 12.5, (13, 6617): 12.5, (13, 6618): 12.5, (13, 6619): 12.5, (13, 6620): 12.5, (13, 6621): 12.5, (13, 6622): 12.5, (13, 6623): 12.5, (13, 6624): 12.5, (13, 6625): 12.5, (13, 6626): 12.5, (13, 6627): 12.5, (13, 6628): 12.5, (13, 6629): 12.5, (13, 6630): 12.5, (13, 6632): 12.5, (13, 6634): 12.5, (13, 6635): 12.5, (13, 6636): 12.5, (13, 6637): 12.5, (13, 6638): 12.5, (13, 6639): 12.5, (13, 6640): 12.5, (13, 6641): 12.5, (13, 6642): 12.5, (13, 6643): 12.5, (13, 6645): 12.5, (13, 6646): 12.5, (13, 6647): 12.5, (13, 6653): 12.5, (13, 6655): 12.5, (13, 6658): 12.5, (13, 6662): 12.5, (13, 6819): 19.533202049360035, (13, 6996): 17.87347733564538, (13, 7059): 15.354851376370618, (13, 7187): 32.677248045421024, (13, 7304): 30.86457469203221, (13, 7528): 23.510357511357505, (13, 7720): 19.820546728616698, (13, 7793): 21.774084284730314, (13, 7807): 21.2292157623998, (13, 7808): 22.246562953555383, (13, 7831): 12.5, (13, 7850): 12.5, (13, 7852): 12.5, (13, 8012): 15.971551918898276, (13, 8125): 34.32998818603075, (13, 8208): 26.086188805403218, (13, 8392): 13.201440415100882, (13, 8651): 39.650548127452616, (13, 9088): 21.226155455983974, (13, 9443): 56.26797645032836, (13, 9444): 55.94096630187634, (13, 9828): 77.20685006218987, (13, 9868): 73.46078588578803, (13, 10180): 35.683560989585764, (13, 10256): 43.43050587962108, (13, 10276): 37.773097300245084, (13, 10378): 32.95581075352963, (13, 10676): 44.3406831714594, (13, 10714): 44.95754475389152, (13, 10730): 37.18934405737156, (13, 10862): 108.1675744554871, (13, 10881): 108.87507446989629, (13, 10883): 109.03280778287727, (13, 10885): 107.9579241860224, (13, 10891): 109.28650306430221, (13, 10909): 108.6591563132321, (13, 10911): 108.17854722962379, (13, 10913): 108.2016859981419, (13, 10915): 107.89478241113513, (13, 10919): 107.74244626863677, (13, 11037): 110.69252525016296, (13, 11039): 106.67374212972662, (13, 11516): 125.29516574015594, (13, 11856): 77.9123357017365, (13, 11857): 77.88350646536696, (13, 11861): 77.91792813639559, (13, 11881): 77.03588016136834, (13, 11902): 75.22916239302886, (13, 11911): 74.57163366239743, (13, 11914): 74.9656496962833, (13, 11922): 76.42375473627011, (13, 11924): 76.76614616409094, (13, 11926): 76.22547755085506, (13, 11950): 76.90700601263087, (13, 11963): 78.6660788188652, (13, 11983): 76.94950440317606, (13, 11985): 79.57708678060695, (13, 12009): 78.77178418367085, (13, 12010): 77.63640845947648, (13, 12018): 77.77963313242854, (13, 12020): 78.18422385718958, (13, 12021): 78.34002150286422, (13, 12024): 79.53051625778983, (13, 12025): 79.22171445694948, (13, 12027): 78.91664043663356, (13, 12031): 77.43086406477876, (13, 12032): 77.91822212336854, (13, 12035): 78.58862269663584, (13, 12041): 80.01113907692684, (13, 12045): 63.072057320834126, (13, 12145): 70.12848973099288, (13, 12275): 98.75076744516124, (13, 12294): 95.50521465928288, (13, 12358): 105.36694946185364, (13, 12463): 109.195982184674, (13, 12465): 109.08343401926852, (13, 12482): 110.74912277197141, (13, 12503): 110.51623154277893, (13, 12506): 110.97231268504022, (13, 12549): 109.99143336731998, (13, 12559): 109.63901714769723, (13, 12569): 110.010132181341, (13, 12572): 110.35361761229198, (13, 12574): 109.63638254649302, (13, 12576): 110.3920269088324, (13, 12591): 110.32986783628293, (13, 12608): 113.14144951342581, (13, 12696): 108.6935801748224, (13, 12710): 111.37350912885445, (13, 12728): 110.02990388906727, (13, 12766): 35.5082189691134, (13, 12771): 31.613780776442173, (13, 12790): 31.16983124778587, (13, 12795): 30.20731600224306, (13, 12797): 25.618723292175655, (13, 12798): 26.21670520944096, (13, 12811): 29.735340351249135, (13, 12830): 28.595353213399267, (13, 12848): 29.147617175703225, (13, 12850): 29.44216992450945, (13, 12852): 28.401792125655533, (13, 12854): 27.862267839468668, (13, 12859): 29.67927899334574, (13, 12861): 26.80378378629044, (13, 12865): 30.433735878437354, (13, 12866): 30.13021768827233, (13, 12867): 31.234108824630642, (13, 12874): 30.7016013843795, (13, 12875): 31.09890391799689, (13, 12881): 29.456420171312587, (13, 12883): 30.120241775176993, (13, 12885): 31.45886180490688, (13, 12888): 29.79225670084808, (13, 12889): 29.625902632807147, (13, 12892): 30.82814715101496, (13, 12893): 29.836316082953715, (13, 12896): 30.137990249053107, (13, 12906): 30.850006219714995, (13, 13018): 28.080931132948717, (13, 13071): 28.870128272230843, (13, 13131): 22.282920080922644, (13, 13146): 25.452550420002453, (13, 13159): 24.202938671991078, (13, 13193): 21.48192241440864, (13, 13198): 14.772592906934365, (13, 13292): 21.800364071516956, (13, 13296): 23.84197620318763, (13, 13406): 12.849971426763156, (13, 13407): 12.904113059328862, (13, 13417): 14.612085947456276, (13, 13418): 15.451176205856989, (13, 13438): 16.0084323368723, (13, 13442): 15.937012632274048, (13, 13443): 15.546316320143404, (13, 13764): 45.33216433795933, (13, 13766): 44.78731194545439, (13, 13771): 46.120750433820184, (13, 13783): 44.49219881382214, (13, 13784): 43.848770331832995, (13, 13792): 48.377213036353, (13, 13824): 45.030299866838085, (13, 14017): 37.37838988609616, (13, 14870): 96.02394277309376, (13, 14997): 35.20632350521925, (13, 15000): 35.67582242021179, (13, 15003): 35.97173759295589, (13, 15006): 33.24352332099674, (13, 15007): 33.078889297533145, (13, 15056): 34.65777638144431, (13, 15063): 35.145799398898795, (13, 15069): 35.80779749630572, (13, 15076): 33.4096408159298, (13, 15086): 33.45590485366064, (13, 15087): 34.39928697983897, (13, 15111): 34.62953566948301, (13, 15116): 34.53833945795936, (13, 15722): 41.827749313926645, (13, 15998): 57.702873987821896, (13, 16073): 139.4405441007555, (13, 16939): 197.16491927415262, (13, 16940): 196.5273899194173, (13, 16951): 197.1293196550373, (13, 16963): 197.2210411644293, (13, 16965): 198.0518813574459, (13, 16969): 197.78611368034294, (13, 16970): 197.545815695518, (13, 16971): 196.8016997018483, (13, 16973): 196.70754074360147, (13, 16974): 198.34341591372026, (13, 16976): 197.63171731600258, (13, 16978): 197.10366889644112, (13, 16980): 197.94490604593275, (13, 16982): 198.29172919056973, (13, 17045): 218.16190147765153, (13, 17048): 219.09866175440692, (13, 17304): 91.50397045493654, (13, 17305): 90.8304214084213, (13, 17330): 91.32964683469586, (13, 17334): 90.66194111537247, (13, 17343): 91.94947976411785, (13, 17345): 90.39558391822325, (13, 17347): 91.1222429949015, (13, 17351): 89.46426902767372, (13, 17372): 90.4735710789513, (13, 17373): 91.93183807989622, (13, 17377): 92.01609980102958, (13, 17382): 91.01632666905842, (13, 17383): 91.27893967965443, (13, 17389): 90.67103350619581, (13, 17400): 91.72523001385345, (13, 17401): 91.74208096714435, (13, 17402): 91.76212015127587, (13, 17403): 91.84320498414588, (13, 17440): 90.21687130307295, (13, 17455): 91.62866578961216, (13, 17491): 91.56748962763602, (13, 17507): 90.65502494780743, (13, 17509): 91.28354985927717, (13, 17590): 88.82260004964444, (13, 17615): 87.48833357793355, (13, 17642): 87.88363537326995, (13, 17643): 87.71540855891568, (13, 17668): 87.54424400601307, (13, 17721): 86.99002333758249, (13, 17754): 92.39899735629805, (13, 17769): 91.15694455855453, (13, 17776): 88.41959073524987, (13, 17804): 92.11801308151519, (13, 17809): 92.68211674731623, (13, 17824): 92.49647125001941, (13, 17837): 90.04045279943375, (13, 17838): 89.9568656712865, (13, 17862): 89.46653226042032, (13, 17866): 90.7424985052025, (13, 17872): 89.14627125184835, (13, 17873): 88.13895951931717, (13, 17881): 89.66301769407889, (13, 17947): 146.7616672613636, (13, 17951): 145.43310201340736, (13, 17953): 145.23823752088393, (13, 17954): 145.3699953387093, (13, 17959): 146.38782741805738, (13, 17963): 145.8191157426257, (13, 18000): 139.23279371284784, (13, 18001): 139.57466672250848, (13, 18111): 161.09936734037962, (13, 18148): 128.60778465491663, (13, 18166): 141.63058836811646, (13, 18189): 152.84139704779915, (13, 18239): 92.30793178477664, (13, 18240): 92.27195252281442, (13, 18245): 92.34611394707986, (13, 18247): 92.19031693230838, (13, 18251): 92.30856672528871, (13, 18256): 92.40314863022066, (13, 18258): 92.24334215779349, (13, 18259): 92.25368449928293, (13, 18260): 92.28776328701895, (13, 18262): 92.37373397281111, (13, 18263): 92.4243505918319, (13, 18264): 92.46003927620573, (13, 18266): 92.39099027873138, (13, 18267): 92.43022692740378, (13, 18268): 92.43904194829129, (13, 18269): 92.51457640512037, (13, 18275): 92.47877882680622, (13, 18285): 92.45919272792726, (13, 18308): 91.6881961973142, (13, 18313): 91.34554162527893, (13, 18314): 91.40596061848294, (13, 18315): 92.58839992261663, (13, 18316): 92.54342787679867, (13, 18317): 92.5763381010768, (13, 18320): 92.66184479748557, (13, 18321): 92.66290044415165, (13, 18322): 92.7224775724203, (13, 18324): 92.82455772216105, (13, 18325): 93.06192172428433, (13, 18326): 92.97520344370176, (13, 18327): 92.57535901550527, (13, 18329): 93.21051158978162, (13, 18330): 92.97563318899262, (13, 18331): 92.83480649062281, (13, 18332): 92.67068446578592, (13, 18333): 92.98383387798508, (13, 18336): 92.9065945132006, (13, 18337): 93.01128972940796, (13, 18403): 92.68241995365973, (13, 18432): 88.4361812641009, (13, 18451): 91.29588296094815, (13, 18466): 94.2347302993688, (13, 18481): 92.7510236205738, (13, 18483): 92.72399082313834, (13, 18484): 92.6143532664551, (13, 18485): 92.31337397029348, (13, 18486): 92.7602804581134, (13, 18487): 92.4923146658812, (13, 18489): 92.63057817773357, (13, 18490): 93.00681748227325, (13, 18491): 93.14916549064426, (13, 18492): 92.1653421870784, (13, 18493): 92.74293794349707, (13, 18494): 92.55057263418269, (13, 18495): 92.90490622582264, (13, 18496): 92.73312390449951, (13, 18497): 92.4567324373626, (13, 18498): 92.41236369971494, (13, 18499): 92.62359830335761, (13, 18501): 92.51965344599378, (13, 18502): 92.38794848402966, (13, 18503): 92.25294693521194, (13, 18504): 92.75818672683059, (13, 18506): 92.62018916328347, (13, 18507): 92.51097132457983, (13, 18508): 92.62090054489467, (13, 18509): 92.64984600713935, (13, 18510): 92.29542540417904, (13, 18511): 92.84067055262611, (13, 18512): 92.62806740922538, (13, 18515): 92.80994871645825, (13, 18516): 92.91156558860396, (13, 18517): 92.78554758769286, (13, 18518): 92.99886770085608, (13, 18519): 92.77180163470562, (13, 18520): 92.54796603748305, (13, 18522): 93.29909911760429, (13, 18523): 93.35827383892452, (13, 18532): 93.59184952133933, (13, 18535): 93.13639329912911, (13, 18537): 92.88282251207544, (13, 18539): 92.95099102078103, (13, 18540): 92.99656380552588, (13, 18541): 93.13469697937357, (13, 18542): 93.21963742187846, (13, 18543): 92.80964322778814, (13, 18546): 93.05406114587056, (13, 18555): 93.45438813724564, (13, 18556): 93.54727314657431, (13, 18565): 93.60139893809712, (13, 18567): 93.77564863578522, (13, 18568): 93.53280872820595, (13, 18577): 95.08600892907464, (13, 18583): 94.74561574231156, (13, 18605): 94.97779020612322, (13, 18608): 94.02772230942134, (13, 18616): 96.43307878016607, (13, 18618): 97.72152794624412, (13, 18625): 97.09311701117178, (13, 18645): 95.91881502787592, (13, 18646): 96.26910988699731, (13, 18653): 95.43124605973466, (13, 18654): 96.43530818935159, (13, 18655): 95.8180626861335, (13, 18666): 99.49649112378285, (13, 18837): 93.1221016846296, (13, 18974): 90.72988054801273, (13, 18999): 91.5104345448057, (13, 19000): 91.87677524849823, (13, 19174): 73.75807648801162, (13, 19342): 81.12493397578726, (13, 19455): 76.88203209971199, (13, 19555): 58.72817876286102, (13, 19564): 60.00906989087926, (13, 19573): 59.173037374968715, (13, 19586): 58.78647468599568, (13, 19605): 59.04247268089663, (13, 19611): 59.59021323277675, (13, 19614): 59.29041227272904, (13, 19641): 68.17861024316369, (13, 19702): 68.09866505319997, (13, 19713): 67.42990102366352, (13, 19731): 55.78889506351247, (13, 19819): 74.04202362964065, (13, 19893): 72.66125485090166, (13, 19899): 77.9405153866572, (13, 19929): 73.58806392661178, (13, 19951): 82.47578014711648, (13, 19962): 75.18699855390724, (13, 19970): 75.38337985319471, (13, 19971): 75.82072351012165, (13, 19972): 75.36739250343658, (13, 19975): 74.73532911075115, (13, 19978): 82.6315578729461, (13, 19987): 82.53681335028364, (13, 19989): 80.09999452640182, (13, 20039): 82.86588917831315, (13, 20043): 83.54900276973675, (13, 20047): 82.47593370824023, (13, 20052): 80.04890529606367, (13, 20054): 80.42043416250996, (13, 20085): 90.51182901206745, (13, 20104): 91.20839995803877, (13, 20132): 87.26164456703091, (13, 20203): 76.12754437293805, (13, 20280): 76.49868956014046, (13, 20285): 76.82498733886428, (13, 20290): 76.64199283270852, (13, 20297): 75.75627166117194, (13, 20309): 85.9420383901019, (13, 20453): 95.81289932712785, (13, 20485): 70.33307182884724, (13, 20520): 68.03922643322383, (13, 20526): 68.74596580980314, (13, 20698): 73.73925331412343, (13, 20868): 95.04140080079608, (13, 21042): 34.607703806396614, (13, 21057): 38.50889894127701, (13, 21066): 37.01737367730786, (13, 21075): 35.63936514116993, (13, 21093): 35.56545555994125, (13, 21098): 39.21893219810997, (13, 21127): 35.27288027288588, (13, 21130): 36.31349509380613, (13, 21144): 35.586111506127935, (13, 21146): 35.023626034271736, (13, 21147): 35.34199568865434, (13, 21148): 36.225504216250975, (13, 21153): 32.460440397431135, (13, 21293): 41.912231663651774, (13, 21426): 37.19365658471326, (13, 21442): 41.891341686803685, (13, 21451): 42.3630006961117, (13, 21466): 39.57234314627947, (13, 21469): 40.33952204358651, (13, 21471): 39.17984510363806, (13, 21473): 39.833717781879, (13, 21475): 39.27054875397236, (13, 21482): 40.76068594645796, (13, 21484): 40.633785363460355, (13, 21488): 40.16714872065549, (13, 21494): 39.36394118128601, (13, 21498): 39.91016941354503, (13, 21500): 39.13217846085292, (13, 21514): 41.10783940062107, (13, 21537): 39.25454790606666, (13, 21662): 42.185398239226714, (13, 21691): 39.327537650336716, (13, 21757): 33.04603040751616, (13, 21777): 30.673971487403154, (13, 21778): 30.16495031003541, (13, 21779): 30.914085218350973, (13, 21790): 30.77384811708245, (13, 21802): 31.628241106283593, (13, 21824): 32.61985492462333, (13, 21874): 31.622512898281578, (13, 21879): 32.21919703075995, (13, 21983): 30.0021561095823, (13, 22002): 39.00354981036685, (13, 22132): 27.77810278884686, (13, 22261): 90.86063862487352, (13, 22298): 90.1813811580162, (13, 22339): 100.12260031778158, (13, 22508): 77.32474663736907, (13, 22841): 228.73065536453498, (13, 22842): 228.75010958181426, (13, 22874): 226.98994208291228, (13, 22941): 227.12132760748327, (13, 22956): 228.24370047614622, (13, 22960): 228.53275845960675, (13, 22968): 229.8447103647775, (13, 22970): 230.1169942674435, (13, 22974): 230.80396879357326, (13, 22980): 232.13730507247305, (13, 23025): 232.2092564966701, (13, 23028): 231.95499434531203, (13, 23081): 234.4675216812512, (13, 23104): 232.46043279933724, (13, 23147): 220.02930110040393, (13, 23298): 54.50298262573845, (13, 23376): 52.49126459430649, (13, 23381): 52.12583951730374, (13, 23529): 56.38852496536164, (13, 23556): 55.135400204018524, (13, 23718): 52.72264765971056, (13, 24001): 66.4858344366035, (13, 24094): 71.25663253463655, (13, 24129): 73.28088230057499, (13, 24174): 69.57707314922321, (13, 24235): 74.3604671409487, (13, 24259): 75.95704701209613, (13, 24260): 75.85976743078925, (13, 24261): 75.3822489176452, (13, 24305): 78.14163779436896, (13, 24306): 78.59248376163633, (13, 24307): 77.96734947652378, (13, 24308): 71.1655641049442, (13, 24498): 82.5590692922876, (13, 24499): 82.61948044611393, (13, 24500): 82.22134174926772, (13, 24668): 78.93082787629437, (13, 24711): 85.51831714679612, (13, 24756): 87.26179776937306, (13, 24788): 87.6932490406775, (13, 24809): 85.80580137728052, (13, 24813): 86.35290905856786, (13, 24821): 86.15567054506332, (13, 24825): 86.3731063313328, (13, 24832): 85.62126640796158, (13, 24833): 85.94720160220187, (13, 24835): 86.29424705288524, (13, 24837): 86.76326646804318, (13, 24840): 85.59794562719033, (13, 24841): 86.04601619279953, (13, 24844): 85.64971130074476, (13, 24845): 85.80420169868393, (13, 24846): 85.97680650192103, (13, 24849): 86.17179298763426, (13, 24850): 86.49606019227635, (13, 24863): 81.70433705704376, (13, 24866): 82.26931795541977, (13, 24885): 83.08192758266294, (13, 24886): 83.21448820643444, (13, 24889): 84.20232134019611, (13, 24903): 84.58084737683761, (13, 24909): 82.25925654041674, (13, 24999): 108.15158660725116, (13, 25019): 107.3167645655654, (13, 25028): 107.80494536282873, (13, 25137): 83.80441700708941, (13, 25145): 84.3229068443485, (13, 25208): 95.84725811278719, (13, 25233): 95.27855765881044, (13, 25371): 80.27989743664577, (13, 25377): 77.62293242379191, (13, 25828): 52.83825821615762, (13, 25851): 47.71287856698664, (13, 25874): 50.39012790180087, (13, 25898): 54.62356014288434, (13, 25946): 52.43093832555318, (13, 26047): 63.870619948638165, (13, 26066): 59.37866856683325, (13, 26197): 59.2531881847467, (13, 26212): 62.26712190565158, (13, 26253): 63.6146825016694, (13, 26254): 62.819999229897626, (13, 26257): 63.23058091374597, (13, 26258): 63.59378374276475, (13, 26260): 63.33892272323359, (13, 26266): 61.85147849056217, (13, 26267): 61.85526192797304, (13, 26271): 62.09303197305048, (13, 26304): 56.8338998084536, (13, 26305): 56.207533846450076, (13, 26363): 56.36589637081709, (13, 26441): 103.51683588880638, (13, 26442): 103.17356500861538, (13, 26450): 102.13377727027999, (13, 26459): 102.57943421250341, (13, 26462): 102.95939756761537, (13, 26467): 106.09448000729476, (13, 26471): 104.94945580139773, (13, 26472): 104.77907096369051, (13, 26473): 104.66853137784256, (13, 26476): 103.40405937284866, (13, 26485): 102.84799530601285, (13, 26493): 102.61097103020435, (13, 26524): 103.66555463791893, (13, 26525): 103.39737659247761, (13, 26556): 104.54964736010498, (13, 26560): 104.88424946579653, (13, 26561): 104.31075175760046, (13, 26564): 104.14080108747918, (13, 26569): 104.00019747224044, (13, 26570): 103.5626875564231, (13, 26573): 103.5008803609985, (13, 26581): 103.2704462435166, (13, 26583): 103.16393548801314, (13, 26593): 103.01902258447411, (13, 26837): 106.10122254345934, (13, 26844): 106.91593170233989, (13, 26863): 104.6490149883015, (13, 26893): 106.79768445412812, (13, 26902): 107.88951693733604, (13, 26905): 107.21912440277497, (13, 26912): 107.93192947033951, (13, 26921): 105.7075914126207, (13, 26922): 102.82855440038121, (13, 27212): 121.92756331632826, (13, 27218): 121.50441586595062, (13, 27239): 123.26513149553794, (13, 27257): 122.34935715537634, (13, 27274): 123.46335079439017, (13, 27279): 123.11877923021629, (13, 27282): 122.28138830911766, (13, 27283): 122.96922720921486, (13, 27285): 123.73308312271006, (13, 27286): 122.6453857061653, (13, 27290): 121.53597108800126, (13, 27295): 121.29731092319285, (13, 27300): 123.68016331994525, (13, 27344): 120.60837845414024, (13, 27366): 121.37850183553084, (13, 27383): 123.42359689332889, (13, 27398): 124.89194593608983, (13, 27406): 124.19100353769515, (13, 27407): 124.58494953742115, (13, 27426): 124.73800464053869, (13, 27432): 120.75252726667134, (13, 27460): 123.42008136419975, (13, 27523): 118.84920862042026, (13, 27545): 137.01778917254907, (13, 27602): 155.30999501578512, (13, 27606): 155.84889141836425, (13, 27646): 132.6599590177859, (13, 27667): 136.4390263145236, (13, 27672): 136.75585521533188, (13, 27674): 136.03725277577448, (13, 27688): 137.0455888935085, (13, 27692): 137.2756133889254, (13, 27693): 136.68396878341878, (13, 27705): 136.52003795176736, (13, 27712): 136.69812273960875, (13, 27786): 160.7233813926803, (13, 27790): 160.16643814500958, (13, 27791): 160.21846196865087, (13, 27795): 159.51643759030102, (13, 27801): 158.95519705595524, (13, 27813): 161.13212213524042, (13, 27816): 160.7490298878124, (13, 27823): 158.94875595185795, (13, 27830): 160.27009422333157, (13, 27884): 124.95361694712065, (13, 27885): 130.86177712949194, (13, 27896): 127.36620983201556, (13, 27919): 127.2583493230238, (13, 27922): 127.79492860324468, (13, 27930): 126.0256753235783, (13, 27934): 126.13202466910141, (13, 27935): 126.16216609508571, (13, 27948): 147.69078381426772, (13, 27951): 150.5803720541785, (13, 28061): 116.51168915868023, (13, 28290): 161.70459863838622, (13, 28292): 162.19049114516199, (13, 28293): 161.76570752956118, (13, 28295): 161.12559522147035, (13, 28296): 161.5181879375423, (13, 28297): 161.41956877131298, (13, 28302): 160.8626529431303, (13, 28310): 162.89198579142297, (13, 28313): 163.3914476754072, (13, 28372): 163.860750985105, (13, 28398): 163.90371852033883, (13, 28399): 163.59404093353194, (13, 28400): 164.0491674596641, (13, 28401): 162.9005841864083, (13, 28445): 162.86695630398637, (13, 28475): 162.25357698550238, (13, 28885): 76.13626836557854, (13, 28886): 75.84437747288105, (13, 28915): 76.51003197800324, (13, 28916): 76.08295185774723, (13, 28917): 75.95713759211313, (13, 28921): 76.76398317216751, (13, 28931): 76.74797543029798, (13, 28945): 76.13846949267149, (13, 28982): 76.14771061413882, (13, 29219): 80.51469016361504, (13, 29228): 78.7669156511652, (13, 29246): 91.36846029120366, (13, 29248): 91.70719683665708, (13, 29282): 89.19058311197607, (13, 29290): 92.05628223495341, (13, 29291): 91.70339918721977, (13, 29292): 92.10115783519714, (13, 29293): 91.14031986455095, (13, 29294): 92.10581860784943, (13, 29298): 91.33818217347866, (13, 29299): 91.38432515408059, (13, 29304): 90.20519573866379, (13, 29317): 87.73581417169844, (13, 29323): 87.52994890334934, (13, 29330): 88.7411973249939, (13, 29331): 89.23772060233907, (13, 29344): 81.706741973951, (13, 29445): 64.93265753151606, (13, 29724): 224.67905285449945, (13, 29738): 225.03597102997315, (13, 29745): 223.95941643760185, (13, 29748): 223.99051549100716, (13, 29750): 224.50234606179836, (13, 29759): 223.5223032406125, (13, 29772): 224.8383580626981, (13, 29781): 224.54610407873105, (13, 29784): 224.39499575768284, (13, 29790): 224.80255054566544, (13, 29811): 223.97873666084317, (13, 29817): 226.00088584208072, (13, 29818): 225.71472620216514, (13, 29929): 223.94708951781425, (13, 30039): 229.13198627343075, (13, 30066): 226.45353196146658, (13, 30116): 213.86642170644586, (13, 30238): 195.32699479264383, (13, 30248): 204.9709154726328, (13, 30260): 205.2285407375932, (13, 30545): 69.10774163131337, (13, 30733): 49.65419399561096, (13, 30756): 47.62019942753191, (13, 30921): 55.154583649844625, (13, 31079): 16.670042237426316, (13, 31149): 12.5, (13, 31154): 12.5, (13, 31160): 12.5, (13, 31163): 12.5, (13, 31189): 12.5, (13, 31215): 12.5, (13, 31259): 15.810892884207378, (13, 31262): 15.82432400045377, (13, 31430): 19.8357858093318, (13, 31568): 29.190193507519222, (13, 31751): 17.76532929763995, (15, 109): 63.595546493209895, (15, 872): 215.26320099463402, (15, 873): 216.1591263977104, (15, 877): 215.81994254591993, (15, 879): 215.95257331884156, (15, 884): 215.045752549473, (15, 889): 215.60876522037398, (15, 891): 214.7499734910058, (15, 892): 216.64780918695456, (15, 894): 216.53590238273043, (15, 896): 215.67790690062785, (15, 903): 215.8502273380418, (15, 909): 214.33508212621908, (15, 910): 214.6970458164869, (15, 912): 214.10380548862292, (15, 913): 213.44891271566297, (15, 916): 213.17671641377092, (15, 926): 214.99528871915805, (15, 927): 214.6953090855491, (15, 948): 214.42560651767548, (15, 961): 214.95545617441863, (15, 962): 215.05938409288194, (15, 963): 215.1754986787776, (15, 967): 216.23028271837188, (15, 974): 215.74293324611375, (15, 998): 216.58257999986876, (15, 1014): 236.20019185088026, (15, 1086): 213.17842753866162, (15, 1087): 213.08189270200057, (15, 1089): 212.247162818662, (15, 1090): 212.62327417986373, (15, 1092): 213.91392397616107, (15, 1097): 212.92632083260185, (15, 1107): 214.56654131341762, (15, 1387): 80.28129149355415, (15, 1554): 66.38601060936172, (15, 1827): 256.1642334594323, (15, 1828): 256.2613756748162, (15, 1829): 256.39813055695583, (15, 1830): 256.2479111811996, (15, 1831): 256.32992608910916, (15, 1832): 256.2338992185346, (15, 1833): 256.2460964123666, (15, 1836): 256.1439682245911, (15, 1841): 256.7180929734138, (15, 1843): 256.4767209035316, (15, 1844): 256.58286323780715, (15, 1845): 256.2943167036238, (15, 1847): 255.36798091103154, (15, 1848): 255.68781642769264, (15, 1849): 257.18558083554785, (15, 1850): 257.343796360448, (15, 1851): 255.92905980832282, (15, 1852): 255.94950424627189, (15, 1854): 256.10506014339376, (15, 1856): 255.3184384860188, (15, 1857): 255.66429666340275, (15, 1858): 257.04192535382185, (15, 1861): 256.3752596652205, (15, 1866): 255.29541378848086, (15, 1867): 256.7373208753265, (15, 1868): 256.54607812214863, (15, 1870): 256.55240928240744, (15, 1871): 256.6961421526522, (15, 1875): 256.0908536112958, (15, 1880): 255.5215641859125, (15, 1882): 255.61183745626056, (15, 1883): 257.3596381597635, (15, 1889): 255.6939816466445, (15, 1893): 256.420671149575, (15, 1894): 256.1950455213785, (15, 1899): 255.49635009239498, (15, 1900): 255.66432667282527, (15, 1902): 256.8136748921701, (15, 1905): 257.10381942823767, (15, 1907): 255.9087332117388, (15, 1910): 256.0202622912276, (15, 1917): 257.7288373970911, (15, 1920): 255.9333331013952, (15, 1935): 257.1496677552709, (15, 1937): 257.3976022221299, (15, 1946): 254.99993962390153, (15, 1949): 255.28009509942027, (15, 1950): 254.29413061217474, (15, 1951): 254.76830474320528, (15, 1952): 255.11472465637252, (15, 1953): 255.27483040408524, (15, 1954): 255.04753626337884, (15, 1958): 255.1977996399488, (15, 1960): 255.66946659671748, (15, 1968): 255.85562790176368, (15, 1969): 257.2124818110297, (15, 1974): 256.8571675095453, (15, 1975): 256.8517878868683, (15, 1979): 256.1822527374299, (15, 1980): 256.1248907681577, (15, 1981): 256.32430643005034, (15, 1985): 256.4875077282886, (15, 1994): 253.90363200478615, (15, 2011): 255.5985352945504, (15, 2019): 257.94271879446745, (15, 2020): 257.6326478547846, (15, 2029): 256.4520938104535, (15, 2030): 257.4177921185212, (15, 2032): 256.25740419923915, (15, 2033): 256.8861472169211, (15, 2034): 256.87363983711117, (15, 2036): 255.68736417623515, (15, 2037): 255.99116856982283, (15, 2038): 256.1003534655911, (15, 2042): 259.6804974417165, (15, 2050): 256.7273811923436, (15, 2051): 256.6738921177938, (15, 2053): 256.76971612689624, (15, 2054): 257.0864095374893, (15, 2066): 256.4416170246303, (15, 2067): 256.4446174382731, (15, 2071): 253.30721777001636, (15, 2072): 253.9021074905128, (15, 2073): 252.27727481070283, (15, 2074): 252.19576236262094, (15, 2080): 251.19038422086237, (15, 2082): 254.2225435858096, (15, 2083): 254.5302548443815, (15, 2089): 253.87958462081417, (15, 2090): 254.1668764224607, (15, 2092): 253.7767548935955, (15, 2098): 251.57583673549124, (15, 2099): 251.92099959633862, (15, 2101): 251.51246109980013, (15, 2102): 253.13391351956795, (15, 2103): 252.6237664064483, (15, 2104): 252.34441487780782, (15, 2106): 254.7372565314424, (15, 2112): 251.72735219364586, (15, 2113): 253.36426206814582, (15, 2114): 253.75392526315923, (15, 2117): 254.9800237052887, (15, 2123): 252.64412060554488, (15, 2124): 252.9784292828078, (15, 2134): 252.0246192740029, (15, 2138): 253.00874642301721, (15, 2141): 252.140825326367, (15, 2148): 252.62676389711967, (15, 2150): 251.32695204033925, (15, 2151): 251.67851148062724, (15, 2152): 251.14182646200234, (15, 2153): 252.7398154147659, (15, 2154): 251.35481110638304, (15, 2155): 251.1949986805909, (15, 2156): 250.9375143432885, (15, 2157): 251.2881364938033, (15, 2160): 253.47444374708243, (15, 2161): 251.0837837894124, (15, 2162): 252.7974742693425, (15, 2163): 252.3278731185606, (15, 2164): 252.2963669331773, (15, 2168): 251.460441284793, (15, 2172): 251.77180042727443, (15, 2174): 251.63763084000954, (15, 2178): 252.0459791069093, (15, 2179): 251.82970953451698, (15, 2183): 252.9854714106691, (15, 2185): 253.00633136690408, (15, 2186): 252.73957973911513, (15, 2190): 253.5402422242582, (15, 2192): 253.0598340872006, (15, 2193): 253.0793095856688, (15, 2194): 252.58863083059603, (15, 2195): 252.51724437726548, (15, 2197): 253.1648960929649, (15, 2205): 252.4778738990571, (15, 2207): 251.58394841447378, (15, 2208): 252.08389069466492, (15, 2212): 253.2236555403198, (15, 2214): 243.31273761202903, (15, 2225): 244.48876849241566, (15, 2231): 242.18469130077267, (15, 2278): 249.3713726396746, (15, 2284): 250.3809281261522, (15, 2285): 250.2396416311523, (15, 2291): 248.2336859976094, (15, 2292): 248.45350176237395, (15, 2307): 249.7244280944393, (15, 2313): 247.9962857018273, (15, 2317): 247.7084476542727, (15, 2319): 248.80077698858224, (15, 2321): 249.26417132748983, (15, 2323): 249.20371960222886, (15, 2326): 250.97140825653463, (15, 2327): 250.53418757055059, (15, 2329): 250.2356536331802, (15, 2330): 249.8953191377743, (15, 2332): 250.61515921166753, (15, 2344): 249.50173545039, (15, 2346): 249.48052678380577, (15, 2361): 249.31923029023545, (15, 2368): 254.41348313831594, (15, 2374): 254.89404127170442, (15, 2375): 255.05545741166986, (15, 2377): 253.37608074180213, (15, 2378): 255.35820626809448, (15, 2379): 255.3996515670968, (15, 2380): 255.56621451840712, (15, 2383): 253.82489299985795, (15, 2385): 254.0846558535239, (15, 2395): 254.11447978436487, (15, 2397): 255.19948115232853, (15, 2398): 252.84097238849452, (15, 2399): 253.4459114266716, (15, 2400): 253.31039125765258, (15, 2402): 254.26700227463354, (15, 2403): 254.6424534758818, (15, 2404): 254.739641361406, (15, 2405): 253.83440893580732, (15, 2407): 254.57254239088812, (15, 2408): 255.01264523405854, (15, 2409): 254.1091808672975, (15, 2411): 254.637749391709, (15, 2412): 254.53995525446751, (15, 2413): 254.8477276091297, (15, 2414): 254.34663876014486, (15, 2422): 254.52271916547653, (15, 2424): 254.6463925467706, (15, 2426): 254.72816601672972, (15, 2433): 254.02743122819786, (15, 2436): 253.83983389558261, (15, 2437): 251.64774105343025, (15, 2440): 252.1312451682786, (15, 2445): 261.8188097353689, (15, 2447): 260.62731826746483, (15, 2454): 261.75031240586344, (15, 2455): 261.81422390957096, (15, 2460): 258.3251099128682, (15, 2461): 258.75541641424866, (15, 2471): 265.70550989328484, (15, 2492): 258.257690076014, (15, 2511): 254.77465823325923, (15, 2523): 256.5554388488732, (15, 2525): 256.0243840501194, (15, 2535): 256.981652211988, (15, 2537): 256.20824258244903, (15, 2538): 256.74527625650995, (15, 2539): 256.50320119741974, (15, 2540): 257.33209305861953, (15, 2542): 257.886250131409, (15, 2559): 268.8982606401841, (15, 2575): 267.88457231678575, (15, 2599): 251.32239088639838, (15, 2600): 255.02815027677931, (15, 2607): 252.90308696429864, (15, 2627): 256.876223735173, (15, 2647): 258.91142000735806, (15, 2674): 257.8759706132142, (15, 2681): 257.58429132101213, (15, 2683): 258.5853847077055, (15, 2686): 257.44339592060834, (15, 2689): 270.7483172225201, (15, 2690): 270.81149762691126, (15, 2713): 273.35613529439513, (15, 2714): 273.5783262198084, (15, 2715): 273.9062290187341, (15, 2739): 273.61589387712064, (15, 2740): 271.5534343786581, (15, 2741): 271.71706438500917, (15, 2749): 273.1614243239016, (15, 2750): 273.2644448240849, (15, 2752): 273.4985261048022, (15, 2755): 273.7575407624462, (15, 2758): 273.6814547768627, (15, 2759): 273.682789902887, (15, 2769): 273.30237215926087, (15, 2771): 272.0811267471377, (15, 2779): 272.1790778343402, (15, 2784): 268.48441291097254, (15, 2800): 269.1445017487713, (15, 2802): 270.91559794859273, (15, 2803): 270.79125773827434, (15, 2804): 270.5722035045908, (15, 2805): 271.19081178215026, (15, 2807): 271.17067310763355, (15, 2809): 271.04781467319265, (15, 2812): 268.9425897584256, (15, 2814): 270.93600199943404, (15, 2817): 271.0095987533223, (15, 2819): 271.21446863109514, (15, 2823): 269.1454064435488, (15, 2832): 271.5981655241136, (15, 2836): 270.12011445444966, (15, 2839): 271.1663288766195, (15, 2841): 271.0816095989456, (15, 2843): 270.9716299708542, (15, 2846): 270.4109389749454, (15, 2849): 271.8283503791973, (15, 2852): 271.4928425441372, (15, 2853): 271.9827718664509, (15, 2876): 272.13159371147367, (15, 2877): 273.31730904056104, (15, 2885): 273.67707819152173, (15, 2918): 271.3849879440004, (15, 2921): 271.89460645139667, (15, 2925): 269.50420326077284, (15, 2926): 268.7070901744292, (15, 2930): 270.5046693488502, (15, 2931): 269.7235361370342, (15, 2938): 271.39084532488107, (15, 2940): 272.8758781795986, (15, 2947): 271.13444809523895, (15, 2949): 270.49072712104305, (15, 2950): 270.7196078565604, (15, 2952): 270.4677324086875, (15, 2958): 270.4188170338717, (15, 2959): 270.662176108676, (15, 2960): 271.2229857338995, (15, 2961): 270.9534154886317, (15, 2963): 270.205202960404, (15, 2968): 270.3652733097007, (15, 2976): 270.1384466375833, (15, 2981): 265.34706452232405, (15, 2982): 265.20965229800976, (15, 2984): 264.9606482910574, (15, 3003): 264.5239034813094, (15, 3046): 261.2577305298494, (15, 3050): 263.82108318591946, (15, 3051): 264.0180361037359, (15, 3053): 263.4683297718088, (15, 3069): 266.5424851206513, (15, 3071): 263.3349761942425, (15, 3080): 273.68648312764856, (15, 3199): 263.72152938782506, (15, 3200): 263.14287719249256, (15, 3205): 266.71912401139775, (15, 3209): 263.44650979169535, (15, 3215): 263.177040284501, (15, 3217): 262.46287334601004, (15, 3249): 263.24019923808567, (15, 3263): 268.6320473632701, (15, 3289): 264.93882906025334, (15, 3301): 265.1148561067651, (15, 3302): 264.85580463381865, (15, 3307): 264.5346580172833, (15, 3310): 265.42228926579054, (15, 3391): 266.2207951751293, (15, 3509): 149.83438665016044, (15, 3510): 149.32383989160746, (15, 3511): 149.66538694292615, (15, 3512): 149.35106113606489, (15, 3514): 149.4598301102431, (15, 3519): 151.02759793064055, (15, 3536): 150.73781673695046, (15, 3545): 151.54073654386175, (15, 3548): 150.76051111806217, (15, 3572): 151.02581040718317, (15, 3581): 150.40345170403478, (15, 3583): 150.0609113791866, (15, 3601): 151.98631917604217, (15, 3656): 151.15898030935935, (15, 3669): 150.17435376866874, (15, 3670): 150.6333450766599, (15, 3695): 148.00837381610617, (15, 3696): 148.3700036712969, (15, 3782): 151.00987680543275, (15, 3792): 150.43564996824037, (15, 3989): 69.7380358860073, (15, 4008): 72.5551813578297, (15, 4031): 72.59123959444854, (15, 4045): 71.38187815603885, (15, 4144): 71.35923554868843, (15, 4145): 68.3910254516724, (15, 4164): 70.23448955774523, (15, 4168): 69.28762573220726, (15, 4173): 69.07659297926087, (15, 4181): 67.3714035240987, (15, 4228): 65.90991531853562, (15, 4248): 65.01940865615872, (15, 4254): 50.20480568804609, (15, 4260): 50.17164336771184, (15, 4262): 51.16286763046876, (15, 4273): 50.90737073224617, (15, 4319): 43.00029907680198, (15, 4326): 42.683421187681546, (15, 4328): 42.73635094869833, (15, 4334): 43.402438080927205, (15, 4335): 43.24341518816673, (15, 4372): 89.42008919464635, (15, 4413): 97.86680424131256, (15, 4434): 88.66129539639734, (15, 4447): 88.08221734288351, (15, 4452): 88.9849963216019, (15, 4463): 86.70824075421241, (15, 4465): 86.43763645185965, (15, 4619): 103.10511876555672, (15, 4645): 103.48686709430645, (15, 4657): 103.87140067785853, (15, 4666): 103.95287915834088, (15, 4676): 104.6862139640527, (15, 4678): 104.58965634625524, (15, 4689): 104.74469793497889, (15, 4704): 108.60103706523743, (15, 4726): 129.5116158781286, (15, 4727): 129.17380088756877, (15, 4730): 128.48513935488614, (15, 4731): 128.90406281485912, (15, 4734): 128.01040801847427, (15, 4735): 127.87988089051419, (15, 4736): 128.20643221439641, (15, 4737): 127.86292197944964, (15, 4738): 128.0723079183073, (15, 4756): 128.51150159365557, (15, 4760): 125.88563707823488, (15, 4761): 125.70372273409468, (15, 4762): 125.6505748065816, (15, 4765): 126.16369431606286, (15, 4773): 129.99257460824202, (15, 4774): 129.99183692329674, (15, 4790): 129.7231443528916, (15, 4795): 129.35290075813998, (15, 4799): 130.29694749248145, (15, 4801): 131.41448197208737, (15, 4804): 129.0920393749636, (15, 4805): 128.79214334470336, (15, 4806): 130.30735474660574, (15, 4815): 130.24941955435156, (15, 4816): 130.95661942767606, (15, 4817): 131.46980892546583, (15, 4826): 130.86076514728225, (15, 4830): 130.53040935837518, (15, 4839): 126.88682819386518, (15, 4840): 127.33730890460956, (15, 4841): 126.74735771899188, (15, 4846): 126.45456826594224, (15, 4848): 126.6790431961751, (15, 4850): 127.03676589622239, (15, 4871): 121.74241987903761, (15, 4883): 125.06720240409238, (15, 4900): 122.93345987135932, (15, 4901): 122.7543270673946, (15, 4917): 109.35252087513668, (15, 4931): 107.41017754896936, (15, 4944): 109.33225705620569, (15, 4956): 108.00801442194482, (15, 4958): 108.43300785303373, (15, 4959): 108.39722129285593, (15, 4961): 108.20420308385137, (15, 4966): 107.81486495704607, (15, 5207): 105.73972986869776, (15, 5272): 54.33676844871868, (15, 5283): 55.09605381638369, (15, 5287): 57.73120945520438, (15, 5289): 58.11956378495931, (15, 5293): 53.07244725045632, (15, 5295): 55.03042821385633, (15, 5296): 55.876673679704446, (15, 5298): 56.33333486923776, (15, 5303): 57.64806508684532, (15, 5305): 55.64463382693031, (15, 5306): 56.370602483995924, (15, 5307): 55.36951240985803, (15, 5308): 56.24223110524546, (15, 5313): 55.10750332761246, (15, 5314): 55.20942727061304, (15, 5317): 56.81866349296616, (15, 5319): 57.18195440237143, (15, 5324): 56.12855354048931, (15, 5326): 55.3991695303887, (15, 5348): 56.97641505118691, (15, 5351): 58.700112849766946, (15, 5399): 59.768525549159996, (15, 5413): 61.481681182529414, (15, 5422): 59.29034380222932, (15, 5445): 58.1068114302948, (15, 5448): 57.47931594723039, (15, 5456): 58.256832446285756, (15, 5467): 59.0796254114585, (15, 5624): 49.54078403768685, (15, 5671): 60.45156372246669, (15, 5672): 59.28407132627197, (15, 5797): 73.96896410361789, (15, 5871): 76.84103498550176, (15, 5976): 69.65103756407484, (15, 6118): 212.12983722055586, (15, 6248): 223.50955879050792, (15, 6345): 38.00681167810077, (15, 6352): 40.58982812082183, (15, 6354): 37.26715742236261, (15, 6359): 36.95020482925594, (15, 6376): 40.66944345450794, (15, 6378): 37.59539038937, (15, 6381): 37.29958284450727, (15, 6383): 38.47771634312868, (15, 6396): 38.42774801561417, (15, 6399): 38.212116808920804, (15, 6408): 40.30517433236567, (15, 6409): 38.61088843516177, (15, 6419): 42.08879472190138, (15, 6422): 39.585343665995175, (15, 6423): 39.76742929155758, (15, 6424): 36.97661402857258, (15, 6439): 37.32400085310992, (15, 6464): 37.89848600254482, (15, 6465): 38.30891614393276, (15, 6469): 38.326228286176566, (15, 6470): 38.56531993633505, (15, 6472): 36.15188684606345, (15, 6480): 35.86383073045635, (15, 6486): 33.58068557601264, (15, 6497): 34.29483286964452, (15, 6503): 36.91491661454644, (15, 6508): 37.15463373148869, (15, 6509): 36.46081215956716, (15, 6521): 35.205663643769554, (15, 6544): 34.948193378524266, (15, 6552): 38.35772949196589, (15, 6553): 38.711953715860915, (15, 6554): 39.07828910317376, (15, 6578): 37.83019299144348, (15, 6582): 37.666657821512665, (15, 6601): 37.57055739028953, (15, 6609): 35.15104378182361, (15, 6610): 34.935607635088886, (15, 6611): 35.15633316599541, (15, 6614): 35.52811615955904, (15, 6615): 35.354176604496814, (15, 6616): 34.588349922329485, (15, 6617): 34.88893845807575, (15, 6618): 33.97204693058776, (15, 6619): 35.732127265168536, (15, 6620): 34.40509784485896, (15, 6621): 34.684678906005274, (15, 6622): 34.73055353693822, (15, 6623): 35.356014172102114, (15, 6624): 35.44420234097849, (15, 6625): 35.600214321126096, (15, 6626): 35.83251873233903, (15, 6627): 35.773907785299194, (15, 6628): 34.29789055235896, (15, 6629): 35.14144013058009, (15, 6630): 36.166579245139644, (15, 6632): 35.27010212130893, (15, 6634): 36.38429521494723, (15, 6635): 34.890641352261255, (15, 6636): 34.509306933814926, (15, 6637): 35.55483044648585, (15, 6638): 35.950426462313985, (15, 6639): 35.62832592895648, (15, 6640): 35.99182740327137, (15, 6641): 34.56114465787275, (15, 6642): 35.82149249305562, (15, 6643): 36.00523672980654, (15, 6645): 35.60309362436929, (15, 6646): 34.22173950533004, (15, 6647): 35.7943556477779, (15, 6653): 35.42665152736545, (15, 6655): 35.68768724718436, (15, 6658): 36.33565138953464, (15, 6662): 35.71165775800506, (15, 6819): 52.23573910283105, (15, 6996): 45.21720333696865, (15, 7059): 40.968127515681054, (15, 7187): 50.43664580236001, (15, 7304): 57.39990157865435, (15, 7528): 45.89592222127638, (15, 7720): 20.506042375598927, (15, 7793): 21.45779727130798, (15, 7807): 20.94281381406962, (15, 7808): 21.72706882552462, (15, 7831): 31.728268751216053, (15, 7850): 28.620898117809663, (15, 7852): 29.78765491877028, (15, 8012): 21.68245609784094, (15, 8125): 25.268544126365207, (15, 8208): 13.092285643549312, (15, 8392): 27.232364472661782, (15, 8651): 72.57264039133584, (15, 9088): 56.11999628261274, (15, 9443): 82.63928649616287, (15, 9444): 82.11096608292165, (15, 9828): 102.72358821502961, (15, 9868): 101.5336202143137, (15, 10180): 25.94617482989143, (15, 10256): 22.765878365558063, (15, 10276): 21.675428571959145, (15, 10378): 15.055174793128733, (15, 10676): 36.659150241148154, (15, 10714): 42.635985447214374, (15, 10730): 35.857439439013376, (15, 10862): 104.73310217618167, (15, 10881): 104.89698341913521, (15, 10883): 105.13875593179965, (15, 10885): 104.63526586837378, (15, 10891): 105.5223378838186, (15, 10909): 104.88596653668972, (15, 10911): 104.2707188835243, (15, 10913): 104.43847877306443, (15, 10915): 104.10736617610036, (15, 10919): 103.85368891565494, (15, 11037): 111.03090466447668, (15, 11039): 108.25711499668242, (15, 11516): 103.0058782478097, (15, 11856): 43.66348202979756, (15, 11857): 43.478034189727005, (15, 11861): 43.585895855935725, (15, 11881): 42.890160565608134, (15, 11902): 41.03442909052626, (15, 11911): 40.53810007963286, (15, 11914): 40.86268834428771, (15, 11922): 42.29900130137223, (15, 11924): 42.69589961989462, (15, 11926): 42.15131449141082, (15, 11950): 43.05690113021011, (15, 11963): 44.83009317244085, (15, 11983): 43.44488711199457, (15, 11985): 45.73137931229725, (15, 12009): 45.21290750314901, (15, 12010): 43.99405216897854, (15, 12018): 44.18027520869355, (15, 12020): 44.54330869598045, (15, 12021): 44.734189982681464, (15, 12024): 45.93393805353037, (15, 12025): 45.56086007522826, (15, 12027): 45.268465150511894, (15, 12031): 43.784963907698945, (15, 12032): 44.228185421661166, (15, 12035): 45.101311812632325, (15, 12041): 46.01204824672187, (15, 12045): 29.124043015758573, (15, 12145): 36.66666480321598, (15, 12275): 71.47942612231384, (15, 12294): 69.0397867539439, (15, 12358): 78.8065982833487, (15, 12463): 82.96211106279961, (15, 12465): 82.88931734269491, (15, 12482): 83.97304609851189, (15, 12503): 83.87228633596509, (15, 12506): 84.28869460477567, (15, 12549): 82.83695856815027, (15, 12559): 82.62428377577436, (15, 12569): 83.16100188624809, (15, 12572): 83.46374245808946, (15, 12574): 82.7702322678328, (15, 12576): 83.13839288028274, (15, 12591): 82.76953009991807, (15, 12608): 85.13757451038613, (15, 12696): 80.83637135587144, (15, 12710): 82.91378161816512, (15, 12728): 82.09591929824656, (15, 12766): 26.1317728786456, (15, 12771): 21.55297735312027, (15, 12790): 21.663669036423556, (15, 12795): 22.468088485590627, (15, 12797): 20.179385618145904, (15, 12798): 19.940984731997993, (15, 12811): 20.072757856823614, (15, 12830): 20.73525011506808, (15, 12848): 19.209033930079176, (15, 12850): 18.287177298125812, (15, 12852): 20.256605310533885, (15, 12854): 20.24689159336975, (15, 12859): 18.837323966636934, (15, 12861): 19.55604868287135, (15, 12865): 20.841167494349648, (15, 12866): 20.34356710976794, (15, 12867): 20.913477571214894, (15, 12874): 20.694932484712616, (15, 12875): 20.558425200679906, (15, 12881): 20.886848724789573, (15, 12883): 20.897790855736933, (15, 12885): 20.72394049489485, (15, 12888): 20.560017212510335, (15, 12889): 20.243513204782918, (15, 12892): 20.889693310978945, (15, 12893): 20.880530836456984, (15, 12896): 20.5909757077983, (15, 12906): 22.112216593161232, (15, 13018): 30.211864099700634, (15, 13071): 32.015618824878935, (15, 13131): 25.645852047281966, (15, 13146): 23.39806867505801, (15, 13159): 33.53422536073946, (15, 13193): 25.345954692276184, (15, 13198): 25.468213820632567, (15, 13292): 21.357419800006817, (15, 13296): 17.6216017447194, (15, 13406): 31.75910364011246, (15, 13407): 32.200342809637355, (15, 13417): 35.06222708350391, (15, 13418): 35.13301420329382, (15, 13438): 31.59494484874839, (15, 13442): 30.406895034113393, (15, 13443): 30.796511830748656, (15, 13764): 79.79723317463545, (15, 13766): 79.21180689232224, (15, 13771): 80.49565017360926, (15, 13783): 79.12390243081126, (15, 13784): 78.26685668183916, (15, 13792): 82.69905808618792, (15, 13824): 79.66865564482983, (15, 14017): 72.25476815703814, (15, 14870): 91.40313405864111, (15, 14997): 53.7392462007032, (15, 15000): 53.80978497134411, (15, 15003): 53.52823301260166, (15, 15006): 51.99177474233948, (15, 15007): 51.57130726555709, (15, 15056): 52.02339516592421, (15, 15063): 52.489106628058906, (15, 15069): 52.800549752180416, (15, 15076): 51.59112144511593, (15, 15086): 52.797644368553556, (15, 15087): 53.42848564393981, (15, 15111): 54.61834953809856, (15, 15116): 53.944392831049605, (15, 15722): 65.49869204269375, (15, 15998): 76.66403274739181, (15, 16073): 174.3964970449116, (15, 16939): 227.62455736063967, (15, 16940): 226.9631036763821, (15, 16951): 227.70807136718432, (15, 16963): 227.773577207912, (15, 16965): 228.58223018222463, (15, 16969): 228.38192974539837, (15, 16970): 228.0678554687595, (15, 16971): 227.3395114612014, (15, 16973): 227.28796531228676, (15, 16974): 228.90466007607162, (15, 16976): 228.1261051998813, (15, 16978): 227.59494738630895, (15, 16980): 228.39778647149586, (15, 16982): 228.89624532305695, (15, 17045): 251.26374467409198, (15, 17048): 252.2022508828114, (15, 17304): 60.905639370848235, (15, 17305): 60.5187488316627, (15, 17330): 60.93425531159158, (15, 17334): 59.98760033751912, (15, 17343): 61.63020088213897, (15, 17345): 60.03312841351361, (15, 17347): 60.9315533442058, (15, 17351): 58.75698921938039, (15, 17372): 59.9138572594596, (15, 17373): 61.56359879880615, (15, 17377): 61.68677129722569, (15, 17382): 60.62905102227127, (15, 17383): 60.797735996180116, (15, 17389): 60.18030053668204, (15, 17400): 61.2433020655546, (15, 17401): 61.2099812359686, (15, 17402): 61.313536853060164, (15, 17403): 61.42559259930434, (15, 17440): 60.206838915604635, (15, 17455): 61.508073890483466, (15, 17491): 61.6903339573655, (15, 17507): 59.257938762651605, (15, 17509): 59.83799502343447, (15, 17590): 58.45419351873778, (15, 17615): 55.10955442405482, (15, 17642): 55.662603307129174, (15, 17643): 55.59425609990786, (15, 17668): 55.10251082841369, (15, 17721): 53.95994571160124, (15, 17754): 59.473296095587095, (15, 17769): 59.44876864051565, (15, 17776): 57.13999222700528, (15, 17804): 60.39812081787999, (15, 17809): 60.98348034709895, (15, 17824): 60.614887984733585, (15, 17837): 58.9287654791932, (15, 17838): 59.016523718396144, (15, 17862): 58.594029829123684, (15, 17866): 59.828941237731044, (15, 17872): 58.15554949321217, (15, 17873): 57.21817891157418, (15, 17881): 58.66098041144993, (15, 17947): 173.603613044699, (15, 17951): 172.34612317781836, (15, 17953): 172.10459818523566, (15, 17954): 172.19184647616032, (15, 17959): 173.34746377632572, (15, 17963): 172.907441583317, (15, 18000): 166.51197012502246, (15, 18001): 166.76015233162966, (15, 18111): 184.8695824754397, (15, 18148): 152.66553248630336, (15, 18166): 165.1976890348133, (15, 18189): 176.74185182982418, (15, 18239): 61.831230249213064, (15, 18240): 61.82970971091763, (15, 18245): 61.88899454977694, (15, 18247): 61.766326473232944, (15, 18251): 61.893649335882955, (15, 18256): 62.03865462688032, (15, 18258): 61.89468118319228, (15, 18259): 61.92468516743976, (15, 18260): 61.98689309497704, (15, 18262): 62.10049880164518, (15, 18263): 62.08090278700102, (15, 18264): 62.14225424447191, (15, 18266): 62.15039980907412, (15, 18267): 62.20993356532905, (15, 18268): 62.24194853910053, (15, 18269): 62.361807348381454, (15, 18275): 62.30524836994237, (15, 18285): 62.11887225903384, (15, 18308): 60.89322579516502, (15, 18313): 60.493540209370686, (15, 18314): 60.685997836138284, (15, 18315): 62.335637881015856, (15, 18316): 62.33540743234369, (15, 18317): 62.39199117688253, (15, 18320): 62.43126958255874, (15, 18321): 62.466638154913355, (15, 18322): 62.553868526706886, (15, 18324): 62.61101113092738, (15, 18325): 62.86856933376175, (15, 18326): 62.77216623275639, (15, 18327): 62.45246516397042, (15, 18329): 62.973708575006825, (15, 18330): 62.875613086023705, (15, 18331): 62.69796608036208, (15, 18332): 62.520392524678094, (15, 18333): 62.8395400209463, (15, 18336): 62.680376643547596, (15, 18337): 62.76193558422537, (15, 18403): 62.689694980212685, (15, 18432): 59.65432292071818, (15, 18451): 61.68248273993668, (15, 18466): 63.75925847816459, (15, 18481): 62.379387768280566, (15, 18483): 62.38533268880459, (15, 18484): 62.239182387287485, (15, 18485): 61.795152427729796, (15, 18486): 62.15626149874865, (15, 18487): 61.822762710089734, (15, 18489): 62.13376349660364, (15, 18490): 62.44771255722299, (15, 18491): 62.60227716731749, (15, 18492): 61.49645927196859, (15, 18493): 62.09592640179319, (15, 18494): 62.07529581130742, (15, 18495): 62.331813748153856, (15, 18496): 62.17385370159841, (15, 18497): 61.74224258274566, (15, 18498): 61.83587829775621, (15, 18499): 62.07856107233302, (15, 18501): 61.894365844571425, (15, 18502): 61.738821334391446, (15, 18503): 61.62506666978328, (15, 18504): 62.24421559002848, (15, 18506): 61.90498092659854, (15, 18507): 61.754831134903384, (15, 18508): 62.039864885831946, (15, 18509): 62.038373802175144, (15, 18510): 61.622672315655294, (15, 18511): 62.13386594132023, (15, 18512): 61.95914436828847, (15, 18515): 62.2515306483804, (15, 18516): 62.24817985267628, (15, 18517): 62.04619828050113, (15, 18518): 62.38000909140221, (15, 18519): 62.28093628499654, (15, 18520): 62.00005340803486, (15, 18522): 62.95303375650409, (15, 18523): 62.979725932267264, (15, 18532): 63.18544690397969, (15, 18535): 62.75109682617414, (15, 18537): 62.50934649441124, (15, 18539): 62.55624061625243, (15, 18540): 62.58060847441056, (15, 18541): 62.69664612259581, (15, 18542): 62.771005540398136, (15, 18543): 62.39909876351127, (15, 18546): 62.56466307793983, (15, 18555): 62.943784457386265, (15, 18556): 63.00872153917802, (15, 18565): 63.148350273015055, (15, 18567): 63.24686713152972, (15, 18568): 63.04522369731103, (15, 18577): 64.53191901468882, (15, 18583): 64.29903887957684, (15, 18605): 64.63358919085508, (15, 18608): 63.35299893834876, (15, 18616): 66.01788863812855, (15, 18618): 67.18762042015479, (15, 18625): 66.83192920699317, (15, 18645): 65.81735305148739, (15, 18646): 66.0678108988092, (15, 18653): 65.03228460394209, (15, 18654): 65.98008819632764, (15, 18655): 65.34727833751701, (15, 18666): 69.2638715975904, (15, 18837): 67.49764306381643, (15, 18974): 62.04023993052177, (15, 18999): 63.26011840530312, (15, 19000): 63.61140401248593, (15, 19174): 50.148732023422966, (15, 19342): 57.757985886270276, (15, 19455): 50.29129668118851, (15, 19555): 36.69736360192716, (15, 19564): 39.86374478190423, (15, 19573): 38.759150400741206, (15, 19586): 38.11052843213838, (15, 19605): 37.95572777136621, (15, 19611): 38.61147242474766, (15, 19614): 37.681606518360034, (15, 19641): 46.00795775866107, (15, 19702): 46.509665278497685, (15, 19713): 45.7601637317737, (15, 19731): 31.082616514982334, (15, 19819): 48.6749209238255, (15, 19893): 40.45606118325148, (15, 19899): 45.78530840821201, (15, 19929): 41.22019129798022, (15, 19951): 49.71012949489357, (15, 19962): 43.10693504163523, (15, 19970): 42.55652329693948, (15, 19971): 43.134878308347375, (15, 19972): 42.82448695399256, (15, 19975): 42.106867494025074, (15, 19978): 49.252669347321365, (15, 19987): 49.077040086651735, (15, 19989): 46.703732596389834, (15, 20039): 49.358552685308666, (15, 20043): 49.917542506409795, (15, 20047): 48.772507600532066, (15, 20052): 46.48802689409517, (15, 20054): 46.90473021887034, (15, 20085): 56.232180944016804, (15, 20104): 56.90821788043849, (15, 20132): 53.17943216586548, (15, 20203): 45.49535537596931, (15, 20280): 46.49027435202867, (15, 20285): 47.0649427440168, (15, 20290): 46.48213695923169, (15, 20297): 45.656151362849045, (15, 20309): 53.409180066004694, (15, 20453): 62.13785844494733, (15, 20485): 40.74025084345802, (15, 20520): 38.64745005749481, (15, 20526): 40.10490019599054, (15, 20698): 107.98950481922486, (15, 20868): 129.8979282558835, (15, 21042): 12.5, (15, 21057): 12.5, (15, 21066): 12.5, (15, 21075): 12.5, (15, 21093): 12.5, (15, 21098): 12.5, (15, 21127): 12.5, (15, 21130): 12.5, (15, 21144): 12.5, (15, 21146): 12.5, (15, 21147): 12.5, (15, 21148): 12.5, (15, 21153): 12.5, (15, 21293): 12.5, (15, 21426): 12.938732224391831, (15, 21442): 18.386084796233202, (15, 21451): 18.88332917383658, (15, 21466): 15.042503179137976, (15, 21469): 15.368309635829025, (15, 21471): 14.912384734495667, (15, 21473): 15.040932120504372, (15, 21475): 14.783698153378001, (15, 21482): 15.989889482382313, (15, 21484): 15.705292058193782, (15, 21488): 15.618472028097576, (15, 21494): 14.19905535440703, (15, 21498): 14.590003716643185, (15, 21500): 13.518921931967, (15, 21514): 12.587921444944243, (15, 21537): 12.5, (15, 21662): 12.5, (15, 21691): 12.5, (15, 21757): 12.5, (15, 21777): 12.5, (15, 21778): 12.649517128343916, (15, 21779): 12.668651748432803, (15, 21790): 12.5, (15, 21802): 12.5, (15, 21824): 12.5, (15, 21874): 13.008329159328975, (15, 21879): 14.144720564185167, (15, 21983): 12.5, (15, 22002): 12.5, (15, 22132): 12.5, (15, 22261): 111.90503458544613, (15, 22298): 110.68552625045443, (15, 22339): 120.24946441972952, (15, 22508): 97.17082396738006, (15, 22841): 263.6199229051598, (15, 22842): 263.63420713348296, (15, 22874): 261.85589002416333, (15, 22941): 262.00559828634925, (15, 22956): 263.1232289929138, (15, 22960): 263.4246771093228, (15, 22968): 264.6580049670079, (15, 22970): 264.94263792838194, (15, 22974): 265.5724891329247, (15, 22980): 266.90484570582174, (15, 23025): 266.8821888372398, (15, 23028): 266.60673846754827, (15, 23081): 268.97540381836205, (15, 23104): 266.73705229123357, (15, 23147): 254.67994589857122, (15, 23298): 22.895456302960547, (15, 23376): 20.735193329392683, (15, 23381): 18.957990405991872, (15, 23529): 23.847514648248687, (15, 23556): 22.645751127883912, (15, 23718): 22.292048793724494, (15, 24001): 35.817095517747866, (15, 24094): 39.07198089844958, (15, 24129): 41.20994951074786, (15, 24174): 36.69225031795248, (15, 24235): 41.410259432568274, (15, 24259): 43.44843091363009, (15, 24260): 43.29119592633084, (15, 24261): 42.83921337865331, (15, 24305): 45.898253019921455, (15, 24306): 46.298705064625146, (15, 24307): 45.68448891475333, (15, 24308): 41.9690545845195, (15, 24498): 51.649930786812064, (15, 24499): 51.684030686163354, (15, 24500): 51.30272246098748, (15, 24668): 49.5727717894324, (15, 24711): 54.087126731085995, (15, 24756): 55.42192576329207, (15, 24788): 56.06196799563764, (15, 24809): 53.64917551134308, (15, 24813): 54.395934606515844, (15, 24821): 54.14966850239647, (15, 24825): 54.33057399755945, (15, 24832): 53.48681637392834, (15, 24833): 53.85073205078537, (15, 24835): 54.21362218635882, (15, 24837): 54.79418743441719, (15, 24840): 53.431339179314925, (15, 24841): 53.992678414185846, (15, 24844): 53.44943697908416, (15, 24845): 53.77812865531761, (15, 24846): 53.75175104954034, (15, 24849): 53.95048176072291, (15, 24850): 54.50649481215477, (15, 24863): 49.43741623305397, (15, 24866): 50.0871920160308, (15, 24885): 50.86156246511066, (15, 24886): 50.92199512661033, (15, 24889): 52.3514350228017, (15, 24903): 52.92065054681426, (15, 24909): 50.54198798878614, (15, 24999): 80.16225040735156, (15, 25019): 79.60164642681137, (15, 25028): 79.70946533096576, (15, 25137): 55.611010264420095, (15, 25145): 55.90634435010268, (15, 25208): 66.86962015726691, (15, 25233): 66.59087316856656, (15, 25371): 50.868364784368566, (15, 25377): 48.45180818939341, (15, 25828): 44.46708449948801, (15, 25851): 44.226043846826, (15, 25874): 42.288054905222054, (15, 25898): 44.57726834972113, (15, 25946): 44.52370893160471, (15, 26047): 47.916886504011615, (15, 26066): 31.99055556215762, (15, 26197): 38.82705201954651, (15, 26212): 65.28434315208598, (15, 26253): 67.47871029074142, (15, 26254): 66.42992398827127, (15, 26257): 66.34298314605691, (15, 26258): 67.23276520586295, (15, 26260): 66.72337750277525, (15, 26266): 66.02936849986686, (15, 26267): 65.65441630219352, (15, 26271): 65.82243647369808, (15, 26304): 57.460828373135456, (15, 26305): 57.015318391068625, (15, 26363): 49.31148986887515, (15, 26441): 118.42276849495433, (15, 26442): 118.15463222862466, (15, 26450): 116.97992122548196, (15, 26459): 117.00087086762505, (15, 26462): 117.21671288392818, (15, 26467): 120.67901889614012, (15, 26471): 119.6504904491505, (15, 26472): 119.53098564286388, (15, 26473): 119.47514496608557, (15, 26476): 118.76251184197997, (15, 26485): 117.53186647554999, (15, 26493): 117.51088806350779, (15, 26524): 117.78900305841606, (15, 26525): 117.62058668465542, (15, 26556): 119.18751033339886, (15, 26560): 119.16970589004973, (15, 26561): 118.44480515094244, (15, 26564): 118.84218128967355, (15, 26569): 118.22995148738009, (15, 26570): 117.8948670004274, (15, 26573): 118.03502123358355, (15, 26581): 117.96521037469128, (15, 26583): 117.73286673081206, (15, 26593): 117.92113250917637, (15, 26837): 120.87067748492902, (15, 26844): 121.68173017563568, (15, 26863): 119.81698476005771, (15, 26893): 122.11066826720071, (15, 26902): 123.20797604546325, (15, 26905): 122.1840895886498, (15, 26912): 123.01274558965947, (15, 26921): 120.92155623853459, (15, 26922): 118.59285685572561, (15, 27212): 129.19985918495613, (15, 27218): 128.38774502068074, (15, 27239): 130.70800847424977, (15, 27257): 129.8527258161644, (15, 27274): 130.99044493003595, (15, 27279): 130.7593627221378, (15, 27282): 129.85553227120536, (15, 27283): 130.32800933731622, (15, 27285): 131.3642452585787, (15, 27286): 130.43318209695406, (15, 27290): 129.07321379648164, (15, 27295): 128.60566643503768, (15, 27300): 131.16975298994055, (15, 27344): 128.48365235572535, (15, 27366): 129.45097273691118, (15, 27383): 131.3202350569435, (15, 27398): 132.56593689054938, (15, 27406): 131.7101994442175, (15, 27407): 132.02469903857238, (15, 27426): 131.2539707371249, (15, 27432): 127.22043532983105, (15, 27460): 129.80483636933005, (15, 27523): 128.9068340142663, (15, 27545): 145.91085914569, (15, 27602): 166.11787320691434, (15, 27606): 166.54810763371268, (15, 27646): 144.23794638378328, (15, 27667): 148.32558562201584, (15, 27672): 148.5721657657901, (15, 27674): 147.85533892477318, (15, 27688): 148.56749838173403, (15, 27692): 149.24240974097393, (15, 27693): 148.6237518321039, (15, 27705): 148.5553227057566, (15, 27712): 148.8291382752068, (15, 27786): 168.39103468419546, (15, 27790): 166.58096400994057, (15, 27791): 166.46049318152973, (15, 27795): 167.20210023415572, (15, 27801): 165.8056097511376, (15, 27813): 168.96667464670864, (15, 27816): 168.31611068069498, (15, 27823): 165.75744407234774, (15, 27830): 167.52425992760018, (15, 27884): 137.03917420400325, (15, 27885): 142.46333943664297, (15, 27896): 139.20372888905203, (15, 27919): 139.01477649902807, (15, 27922): 139.63729269505583, (15, 27930): 137.9088646375797, (15, 27934): 138.0851350721389, (15, 27935): 138.20270072737796, (15, 27948): 162.51572103061477, (15, 27951): 164.10823427610976, (15, 28061): 140.73167559228, (15, 28290): 184.46115972383143, (15, 28292): 185.23987969902012, (15, 28293): 184.60347060332717, (15, 28295): 184.1554327262823, (15, 28296): 184.37670740380696, (15, 28297): 184.0401512363614, (15, 28302): 183.6573164538077, (15, 28310): 196.0387693738914, (15, 28313): 196.686152556952, (15, 28372): 196.86663485583148, (15, 28398): 196.93203529589198, (15, 28399): 196.64142630118457, (15, 28400): 197.1045077214815, (15, 28401): 195.89719106699795, (15, 28445): 196.24442180323732, (15, 28475): 195.01500358730232, (15, 28885): 41.73631967275596, (15, 28886): 41.38798551855367, (15, 28915): 41.91337897655326, (15, 28916): 41.52097364801827, (15, 28917): 41.356509304290846, (15, 28921): 42.42995940846405, (15, 28931): 42.36347728855403, (15, 28945): 41.26156904256393, (15, 28982): 41.39244190722893, (15, 29219): 45.490401106807376, (15, 29228): 43.74215530110831, (15, 29246): 56.35053620529637, (15, 29248): 56.71227462698134, (15, 29282): 54.19785883778353, (15, 29290): 57.03182919247235, (15, 29291): 56.678699964597016, (15, 29292): 57.07637700235448, (15, 29293): 56.11552188432987, (15, 29294): 57.082173636009784, (15, 29298): 56.31394087045687, (15, 29299): 56.36180344621326, (15, 29304): 55.1803973621733, (15, 29317): 52.71138939671584, (15, 29323): 52.505709714482066, (15, 29330): 53.71649838315827, (15, 29331): 54.21347633548045, (15, 29344): 46.71300156422772, (15, 29445): 31.51256431120186, (15, 29724): 259.6968017605573, (15, 29738): 260.0535773203163, (15, 29745): 258.979078212407, (15, 29748): 259.014987168224, (15, 29750): 259.52713363235756, (15, 29759): 258.54654705015224, (15, 29772): 259.8624907900274, (15, 29781): 259.5703380984485, (15, 29784): 259.4176266605848, (15, 29790): 259.8271317148987, (15, 29811): 259.0034246537761, (15, 29817): 261.00420386626274, (15, 29818): 260.7171785300394, (15, 29929): 258.96083520146453, (15, 30039): 264.08609404917075, (15, 30066): 261.3585413399918, (15, 30116): 248.85008482485176, (15, 30238): 230.35178951813342, (15, 30248): 239.93000431969162, (15, 30260): 240.17914001324675, (15, 30545): 35.254901313835376, (15, 30733): 15.9715865216806, (15, 30756): 12.667819427558674, (15, 30921): 20.50280304714256, (15, 31079): 45.29178046922061, (15, 31149): 42.024552435913535, (15, 31154): 42.72869383465394, (15, 31160): 42.01360550885501, (15, 31163): 42.89121657307158, (15, 31189): 46.40433167978441, (15, 31215): 46.72224052016546, (15, 31259): 50.2177672090247, (15, 31262): 50.450676108383774, (15, 31430): 47.49291466396105, (15, 31568): 63.892142653756956, (15, 31751): 48.85056415930336, (16, 109): 76.13929927394126, (16, 872): 114.13444369195987, (16, 873): 115.06761128466255, (16, 877): 114.89483745511947, (16, 879): 115.05052081829416, (16, 884): 114.51379923746725, (16, 889): 115.01256979742791, (16, 891): 114.15728169784535, (16, 892): 115.73702063789787, (16, 894): 115.54666310834752, (16, 896): 114.3540881214127, (16, 903): 115.13329884532949, (16, 909): 112.96251383440104, (16, 910): 113.17262134574874, (16, 912): 112.5939518462372, (16, 913): 112.01700535863279, (16, 916): 111.53341282579734, (16, 926): 113.26502252709336, (16, 927): 112.91537650251668, (16, 948): 113.79061601995421, (16, 961): 113.61269843011075, (16, 962): 113.60455558015546, (16, 963): 113.63246122562005, (16, 967): 115.45514502648643, (16, 974): 115.373002871404, (16, 998): 115.97082891986119, (16, 1014): 134.37396392243102, (16, 1086): 107.3162936595096, (16, 1087): 106.68038275119605, (16, 1089): 106.08972050687541, (16, 1090): 106.5256143526104, (16, 1092): 107.87188834690023, (16, 1097): 106.9476794339322, (16, 1107): 108.21647752388974, (16, 1387): 38.685816558910325, (16, 1554): 52.725477226764774, (16, 1827): 160.53921038498112, (16, 1828): 160.55970083983647, (16, 1829): 160.7574832890211, (16, 1830): 160.98184170839687, (16, 1831): 160.99936830224866, (16, 1832): 160.86226359866527, (16, 1833): 160.8095300365677, (16, 1836): 160.629310609601, (16, 1841): 161.3247626492689, (16, 1843): 161.07278234258933, (16, 1844): 161.24849742049665, (16, 1845): 161.00443574391662, (16, 1847): 159.84541821379864, (16, 1848): 160.20289240894138, (16, 1849): 161.9416144342832, (16, 1850): 162.05795966568635, (16, 1851): 160.64694537417654, (16, 1852): 160.82085995786437, (16, 1854): 160.87478184639556, (16, 1856): 159.99051371203714, (16, 1857): 160.2592156093181, (16, 1858): 161.6764388509976, (16, 1861): 160.86198658867823, (16, 1866): 160.09609698603978, (16, 1867): 161.2176850369566, (16, 1868): 160.89492624676544, (16, 1870): 161.4114791868683, (16, 1871): 161.04802204731953, (16, 1875): 160.75684404812233, (16, 1880): 160.07947511205714, (16, 1882): 160.39515490588082, (16, 1883): 161.90374463499373, (16, 1889): 160.01548246169764, (16, 1893): 160.53605684881725, (16, 1894): 160.25347965649837, (16, 1899): 159.7023231890481, (16, 1900): 159.8294852747992, (16, 1902): 160.9537636330963, (16, 1905): 161.36028353327353, (16, 1907): 160.28626207316003, (16, 1910): 160.2188381812707, (16, 1917): 161.53638144192107, (16, 1920): 160.17971840790597, (16, 1935): 161.12097134997623, (16, 1937): 161.4334789359722, (16, 1946): 158.8357599508672, (16, 1949): 159.05193793432875, (16, 1950): 158.40206794784024, (16, 1951): 158.79633441391573, (16, 1952): 159.5460435134336, (16, 1953): 159.35290900432867, (16, 1954): 159.37969057901137, (16, 1958): 159.1278500569437, (16, 1960): 159.71478622922604, (16, 1968): 159.94553701815988, (16, 1969): 160.89780960833752, (16, 1974): 160.67384505860528, (16, 1975): 160.76541733420757, (16, 1979): 159.89112622747325, (16, 1980): 160.1231008975879, (16, 1981): 160.14349449862195, (16, 1985): 160.22917706093978, (16, 1994): 158.67737705355418, (16, 2011): 160.48203218212143, (16, 2019): 163.30089027772928, (16, 2020): 162.93034288568163, (16, 2029): 161.8076921829302, (16, 2030): 162.66893305326073, (16, 2032): 161.7717593085985, (16, 2033): 162.22368680060214, (16, 2034): 162.35703766915557, (16, 2036): 161.7883328675516, (16, 2037): 161.90979280390493, (16, 2038): 161.33256583921127, (16, 2042): 165.14497921635342, (16, 2050): 161.8430318942884, (16, 2051): 161.94295995903454, (16, 2053): 161.97605121066894, (16, 2054): 162.31858688071782, (16, 2066): 161.64881693108677, (16, 2067): 161.57167563680653, (16, 2071): 157.96674700580382, (16, 2072): 158.47460269076583, (16, 2073): 156.3729749996588, (16, 2074): 156.3866081419363, (16, 2080): 155.58642053606664, (16, 2082): 158.78322447394586, (16, 2083): 159.0367694104559, (16, 2089): 158.25242040030008, (16, 2090): 158.46299037993933, (16, 2092): 157.97356438054155, (16, 2098): 155.78718359036395, (16, 2099): 156.23601737280453, (16, 2101): 155.85799145416527, (16, 2102): 157.35228454301432, (16, 2103): 156.9373391648209, (16, 2104): 156.77481197672233, (16, 2106): 159.31063467220187, (16, 2112): 156.18337938950813, (16, 2113): 157.6485358447557, (16, 2114): 158.2439259955764, (16, 2117): 159.6560910306944, (16, 2123): 152.21205938913977, (16, 2124): 152.52439049253456, (16, 2134): 151.9696917421739, (16, 2138): 152.75361890639115, (16, 2141): 151.9744493283724, (16, 2148): 153.7468348464222, (16, 2150): 151.27774639760258, (16, 2151): 151.70173514674104, (16, 2152): 151.19446165199793, (16, 2153): 153.72493929776118, (16, 2154): 152.35288194238794, (16, 2155): 152.43055584544692, (16, 2156): 152.02912548766045, (16, 2157): 153.18584075414654, (16, 2160): 153.81778098300805, (16, 2161): 151.27083126733075, (16, 2162): 154.28560577274965, (16, 2163): 153.80396947069977, (16, 2164): 153.85643670771785, (16, 2168): 152.07825433509976, (16, 2172): 152.97904342027783, (16, 2174): 151.82880776280334, (16, 2178): 153.41434341707753, (16, 2179): 153.26420752016642, (16, 2183): 152.88253772003955, (16, 2185): 152.9826751665467, (16, 2186): 152.69085751430077, (16, 2190): 153.7357757897134, (16, 2192): 153.23819032306048, (16, 2193): 152.92511850188626, (16, 2194): 152.41732876087713, (16, 2195): 152.51659139120133, (16, 2197): 153.43202784699204, (16, 2205): 152.968059523967, (16, 2207): 152.3115476655012, (16, 2208): 152.71340990648758, (16, 2212): 152.69735321840588, (16, 2214): 145.66483701056598, (16, 2225): 147.34811623486118, (16, 2231): 141.24501281859995, (16, 2278): 153.3834790708216, (16, 2284): 154.69100258752584, (16, 2285): 154.67402176709717, (16, 2291): 153.51138578981065, (16, 2292): 152.7289886749918, (16, 2307): 154.06227378401482, (16, 2313): 153.59124519065674, (16, 2317): 151.58644001552935, (16, 2319): 153.17269535505574, (16, 2321): 153.7986996727139, (16, 2323): 153.45869526498385, (16, 2326): 154.70737115722648, (16, 2327): 154.2691334697745, (16, 2329): 153.99848997074835, (16, 2330): 153.7553957781473, (16, 2332): 154.6066291075749, (16, 2344): 153.0927552665656, (16, 2346): 153.2647773277171, (16, 2361): 151.50535184343676, (16, 2368): 157.5348491220601, (16, 2374): 158.16497826641884, (16, 2375): 158.2328091729508, (16, 2377): 156.39812223434114, (16, 2378): 158.61971946133573, (16, 2379): 158.8527524777437, (16, 2380): 158.88586482538923, (16, 2383): 156.73641442994452, (16, 2385): 156.93318828156347, (16, 2395): 156.79510801817088, (16, 2397): 158.73632514492783, (16, 2398): 155.83467958104438, (16, 2399): 156.36228093185989, (16, 2400): 156.2203323205856, (16, 2402): 157.72847856307564, (16, 2403): 158.12462940740593, (16, 2404): 158.14872645234777, (16, 2405): 157.26417272607546, (16, 2407): 157.87187252079437, (16, 2408): 158.41743969557393, (16, 2409): 157.50269836475837, (16, 2411): 158.439080526231, (16, 2412): 158.21598183466972, (16, 2413): 158.5844547773097, (16, 2414): 158.09957399443903, (16, 2422): 158.4296420943094, (16, 2424): 158.25812440043944, (16, 2426): 158.27938810235216, (16, 2433): 157.6681796622695, (16, 2436): 157.681200501189, (16, 2437): 155.32428731383922, (16, 2440): 155.7867004052275, (16, 2445): 167.66559367954412, (16, 2447): 166.2365000427789, (16, 2454): 167.4037001835297, (16, 2455): 167.31492050619136, (16, 2460): 163.8965681940038, (16, 2461): 164.35202242417756, (16, 2471): 172.42102066050504, (16, 2492): 171.12844563885992, (16, 2511): 166.50128808255627, (16, 2523): 168.89094416529085, (16, 2525): 168.71351217426948, (16, 2535): 166.23016951257586, (16, 2537): 165.55166367774171, (16, 2538): 165.85935974834678, (16, 2539): 166.4273559157057, (16, 2540): 166.5583503051402, (16, 2542): 167.32672367477952, (16, 2559): 176.57770286316307, (16, 2575): 176.5074803436142, (16, 2599): 157.90435313630633, (16, 2600): 162.09739854795217, (16, 2607): 159.0823661218714, (16, 2627): 171.58845205678517, (16, 2647): 174.1955049098029, (16, 2674): 172.24390269166943, (16, 2681): 172.3985581075866, (16, 2683): 173.19584453188753, (16, 2686): 171.84102791465435, (16, 2689): 185.5460729027845, (16, 2690): 185.7149084112249, (16, 2713): 191.44023521453084, (16, 2714): 192.09827839550587, (16, 2715): 192.4033503339404, (16, 2739): 192.00455491134093, (16, 2740): 188.8689891052402, (16, 2741): 188.93597790879633, (16, 2749): 192.04139756497054, (16, 2750): 191.9822867680015, (16, 2752): 192.13001033417498, (16, 2755): 192.4696797304661, (16, 2758): 192.52912064875906, (16, 2759): 192.46061428630279, (16, 2769): 191.9284445787419, (16, 2771): 189.6781768404986, (16, 2779): 190.89819440347438, (16, 2784): 187.91917106360057, (16, 2800): 189.66714384480798, (16, 2802): 188.86998500470548, (16, 2803): 188.61166217920407, (16, 2804): 188.34911791847816, (16, 2805): 189.556168567459, (16, 2807): 189.39399577200575, (16, 2809): 189.5978054023138, (16, 2812): 187.24791783568037, (16, 2814): 190.44338360005204, (16, 2817): 191.80473574920413, (16, 2819): 189.08545857797998, (16, 2823): 188.68349352908143, (16, 2832): 190.1436140707176, (16, 2836): 188.72693588269172, (16, 2839): 189.24480745318056, (16, 2841): 191.21703196915524, (16, 2843): 190.88133810312956, (16, 2846): 189.58521430862987, (16, 2849): 190.6058660332638, (16, 2852): 190.19265650015953, (16, 2853): 190.80487829949098, (16, 2876): 191.61583197506405, (16, 2877): 192.84987064159986, (16, 2885): 194.55925263417933, (16, 2918): 188.33894028147157, (16, 2921): 188.9996857790124, (16, 2925): 185.44400909720443, (16, 2926): 183.99821816694924, (16, 2930): 187.9934631006188, (16, 2931): 186.04531011557623, (16, 2938): 188.59130316811, (16, 2940): 188.87184090357601, (16, 2947): 186.87538380760876, (16, 2949): 187.42063638677985, (16, 2950): 187.88493298188374, (16, 2952): 187.64805799883666, (16, 2958): 187.50058398210376, (16, 2959): 187.45548354129235, (16, 2960): 188.09323877898504, (16, 2961): 187.94290072142695, (16, 2963): 187.4345078222823, (16, 2968): 187.7342306980817, (16, 2976): 187.2222001510723, (16, 2981): 184.39223069408692, (16, 2982): 184.557687554705, (16, 2984): 184.39040758200971, (16, 3003): 184.30607155504916, (16, 3046): 177.84953124753622, (16, 3050): 181.86756789770456, (16, 3051): 181.94223365280345, (16, 3053): 181.54520159970505, (16, 3069): 184.94271175875173, (16, 3071): 180.7479984398053, (16, 3080): 195.06146162350962, (16, 3199): 185.37380404418863, (16, 3200): 185.04180398784493, (16, 3205): 188.17702994866386, (16, 3209): 185.35597831596314, (16, 3215): 184.90767511449948, (16, 3217): 184.29447338301475, (16, 3249): 184.78779958991322, (16, 3263): 189.36374265522838, (16, 3289): 185.78356966976483, (16, 3301): 186.36313414384873, (16, 3302): 185.98225249439437, (16, 3307): 185.6601660213195, (16, 3310): 186.62850281449388, (16, 3391): 195.66267997363985, (16, 3509): 85.21670018633249, (16, 3510): 84.89118232690225, (16, 3511): 84.79640098660114, (16, 3512): 84.32202222770997, (16, 3514): 84.14361909271008, (16, 3519): 87.50328964205276, (16, 3536): 85.24904025455746, (16, 3545): 85.45674909405845, (16, 3548): 84.54248422072256, (16, 3572): 85.81307069438864, (16, 3581): 86.44912633109611, (16, 3583): 84.94771066961748, (16, 3601): 88.601531528288, (16, 3656): 89.25383952147824, (16, 3669): 91.19179586996108, (16, 3670): 91.58887294829283, (16, 3695): 88.8800745294989, (16, 3696): 89.05770616486406, (16, 3782): 79.30985748400329, (16, 3792): 79.75246426623778, (16, 3989): 187.19268385520576, (16, 4008): 190.04831197314894, (16, 4031): 190.35479531506832, (16, 4045): 188.8728977662125, (16, 4144): 188.56370313303336, (16, 4145): 185.1862593564843, (16, 4164): 187.3407227935421, (16, 4168): 186.21153501461131, (16, 4173): 185.910479934182, (16, 4181): 184.17008106672677, (16, 4228): 183.06400891443417, (16, 4248): 181.61870532277138, (16, 4254): 163.56706987135502, (16, 4260): 163.88946283749405, (16, 4262): 164.73392657459732, (16, 4273): 164.6819508740023, (16, 4319): 153.58327810759175, (16, 4326): 153.32511761002226, (16, 4328): 153.53179893513314, (16, 4334): 153.91855833118552, (16, 4335): 153.63040606911662, (16, 4372): 117.21041356373115, (16, 4413): 124.25135295432042, (16, 4434): 117.09553258342234, (16, 4447): 118.73107643746901, (16, 4452): 117.10335132238382, (16, 4463): 97.34063135778848, (16, 4465): 98.12521517761103, (16, 4619): 123.38457061707479, (16, 4645): 125.56547216619012, (16, 4657): 125.04302268004083, (16, 4666): 124.10389467389066, (16, 4676): 125.44561146591477, (16, 4678): 125.84870864587964, (16, 4689): 124.67463384265702, (16, 4704): 131.30172461045007, (16, 4726): 143.09662070087617, (16, 4727): 142.8520377638899, (16, 4730): 142.3919715873063, (16, 4731): 142.43429040305094, (16, 4734): 143.21738964869613, (16, 4735): 142.90850116596363, (16, 4736): 142.9567154070909, (16, 4737): 142.45509586835678, (16, 4738): 142.4549053116857, (16, 4756): 142.65716457965738, (16, 4760): 141.8261400866815, (16, 4761): 142.12156519833388, (16, 4762): 141.39965949708855, (16, 4765): 141.89790680492294, (16, 4773): 143.65320894426844, (16, 4774): 143.30384035646276, (16, 4790): 143.51012921884268, (16, 4795): 143.32939156245413, (16, 4799): 143.34097790718653, (16, 4801): 143.67984801199063, (16, 4804): 143.57786935783378, (16, 4805): 143.42816721599436, (16, 4806): 143.01897537398034, (16, 4815): 142.66960928619537, (16, 4816): 143.3446848256885, (16, 4817): 143.31945370622586, (16, 4826): 142.99682992913233, (16, 4830): 142.58376724070342, (16, 4839): 142.52318535282802, (16, 4840): 142.67295620333297, (16, 4841): 142.10769488547683, (16, 4846): 141.96609429237253, (16, 4848): 141.77659738200686, (16, 4850): 141.9743111069979, (16, 4871): 139.81446794152922, (16, 4883): 141.7531635378989, (16, 4900): 140.94937259517715, (16, 4901): 140.54004786933453, (16, 4917): 120.2375762292916, (16, 4931): 118.35029925693203, (16, 4944): 120.56384672136143, (16, 4956): 118.5828052574848, (16, 4958): 118.3060022799776, (16, 4959): 117.79555746917532, (16, 4961): 119.05597276082436, (16, 4966): 117.9924117148557, (16, 5207): 115.88293774156, (16, 5272): 94.18748094858266, (16, 5283): 94.55163448774505, (16, 5287): 94.24181701960916, (16, 5289): 94.37735913122799, (16, 5293): 95.16727640542716, (16, 5295): 96.31531855423513, (16, 5296): 95.74949328652065, (16, 5298): 95.42602685371307, (16, 5303): 95.30845438956739, (16, 5305): 92.85351142084099, (16, 5306): 91.73564065468987, (16, 5307): 92.59328895692325, (16, 5308): 92.85973961451074, (16, 5313): 93.55210718607627, (16, 5314): 94.02323224365387, (16, 5317): 92.49732384421395, (16, 5319): 94.7620159724106, (16, 5324): 94.94583529267916, (16, 5326): 95.10085659388128, (16, 5348): 91.15633779705222, (16, 5351): 90.68788608414282, (16, 5399): 93.8311310840391, (16, 5413): 90.03634747229778, (16, 5422): 94.60602579872906, (16, 5445): 93.36218125418326, (16, 5448): 92.9420883005805, (16, 5456): 92.25895221672278, (16, 5467): 92.4985357943386, (16, 5624): 90.12414607192312, (16, 5671): 110.9250368196174, (16, 5672): 110.38350758230742, (16, 5797): 118.32129844887997, (16, 5871): 95.9553610934884, (16, 5976): 89.77881922213088, (16, 6118): 152.31376912163168, (16, 6248): 168.00393341821493, (16, 6345): 104.37215778531836, (16, 6352): 103.75548856373177, (16, 6354): 104.30498609994177, (16, 6359): 104.83658482275911, (16, 6376): 104.85241236689072, (16, 6378): 104.2734004891297, (16, 6381): 105.0623344666, (16, 6383): 104.07494902205032, (16, 6396): 106.59117926503892, (16, 6399): 104.8680417786742, (16, 6408): 103.3664240561898, (16, 6409): 102.58227658971161, (16, 6419): 99.8922246449272, (16, 6422): 102.59633790059654, (16, 6423): 102.48612350285448, (16, 6424): 103.04731794439839, (16, 6439): 102.57562586317978, (16, 6464): 102.0573839137388, (16, 6465): 102.35690067022, (16, 6469): 103.21375209422986, (16, 6470): 103.35329067305675, (16, 6472): 105.22012396166924, (16, 6480): 103.3267314426673, (16, 6486): 101.9347376306266, (16, 6497): 102.30526260860918, (16, 6503): 99.9795920856286, (16, 6508): 101.17392964497137, (16, 6509): 100.79140858903601, (16, 6521): 102.63577217554517, (16, 6544): 101.50137466847868, (16, 6552): 100.80451181242125, (16, 6553): 100.58306380445534, (16, 6554): 100.37341867111653, (16, 6578): 101.33708333958405, (16, 6582): 100.04558937716415, (16, 6601): 101.19288525929711, (16, 6609): 103.94178920821058, (16, 6610): 103.7570875201292, (16, 6611): 104.41307067058617, (16, 6614): 104.68544130231051, (16, 6615): 104.50382345818744, (16, 6616): 103.8970094296657, (16, 6617): 104.0930365298936, (16, 6618): 103.56163622839387, (16, 6619): 104.42569669862131, (16, 6620): 103.51801810591489, (16, 6621): 103.27909258731415, (16, 6622): 103.58223387140686, (16, 6623): 104.24836686455824, (16, 6624): 103.70446665326322, (16, 6625): 103.88257862363605, (16, 6626): 104.58545898732588, (16, 6627): 104.98378838019565, (16, 6628): 103.0947180524428, (16, 6629): 103.27599282580442, (16, 6630): 104.36658764775673, (16, 6632): 103.47330479050999, (16, 6634): 103.95061535445312, (16, 6635): 103.42895570095065, (16, 6636): 103.77328549427938, (16, 6637): 103.0153403687714, (16, 6638): 104.0179151966888, (16, 6639): 104.77495098998068, (16, 6640): 104.23954535150682, (16, 6641): 102.97479603110584, (16, 6642): 103.76449377855869, (16, 6643): 104.8427481262282, (16, 6645): 104.27239463788126, (16, 6646): 103.80457448309245, (16, 6647): 103.95451324711269, (16, 6653): 104.61527751091819, (16, 6655): 104.9019826519143, (16, 6658): 103.78780568314542, (16, 6662): 103.4795263824153, (16, 6819): 90.00842585222597, (16, 6996): 86.66993227944286, (16, 7059): 89.05771875428808, (16, 7187): 72.35559924976245, (16, 7304): 74.98824593768471, (16, 7528): 80.94298500082445, (16, 7720): 101.27683647416457, (16, 7793): 99.16438341828588, (16, 7807): 99.97514324937674, (16, 7808): 98.67563250576423, (16, 7831): 102.54417181141028, (16, 7850): 106.71588252577291, (16, 7852): 106.69566142447661, (16, 8012): 102.97612217364417, (16, 8125): 93.96855873566244, (16, 8208): 106.53596483371817, (16, 8392): 98.72654884890046, (16, 8651): 82.3324648911619, (16, 9088): 97.6260581343188, (16, 9443): 56.40127642877405, (16, 9444): 56.187651123611616, (16, 9828): 44.25371260029709, (16, 9868): 54.47430034838065, (16, 10180): 93.58983034062564, (16, 10256): 101.62587802057452, (16, 10276): 99.03810310744774, (16, 10378): 104.11822015465442, (16, 10676): 84.86825544537683, (16, 10714): 77.65414104538687, (16, 10730): 83.18750624277557, (16, 10862): 56.23454459363588, (16, 10881): 57.93883573857469, (16, 10883): 57.72322726695619, (16, 10885): 55.87518605118931, (16, 10891): 57.391993808633416, (16, 10909): 57.304009259527625, (16, 10911): 57.611979699232286, (16, 10913): 57.19595602297525, (16, 10915): 57.21523322455551, (16, 10919): 57.48429310450618, (16, 11037): 45.531570770846706, (16, 11039): 41.24931421300564, (16, 11516): 221.8133629574461, (16, 11856): 154.15737853547944, (16, 11857): 153.3159898143794, (16, 11861): 153.74005932050508, (16, 11881): 153.92018656722277, (16, 11902): 152.20366340423416, (16, 11911): 152.3603610100327, (16, 11914): 152.39425552256412, (16, 11922): 153.50695327393518, (16, 11924): 154.03094864509282, (16, 11926): 153.5640190180853, (16, 11950): 155.04937142059399, (16, 11963): 156.5921919279191, (16, 11983): 156.32802815125493, (16, 11985): 157.32615486144638, (16, 12009): 157.7078414774891, (16, 12010): 156.440170528153, (16, 12018): 156.71486156222545, (16, 12020): 156.91358992452024, (16, 12021): 157.17205213913164, (16, 12024): 158.22627386448121, (16, 12025): 157.72891057324853, (16, 12027): 157.51401550860666, (16, 12031): 156.25196938363732, (16, 12032): 156.50869831223926, (16, 12035): 157.7968767312533, (16, 12041): 157.056346874522, (16, 12045): 143.20344723019852, (16, 12145): 150.62964497914538, (16, 12275): 189.47568186352794, (16, 12294): 187.40036958540196, (16, 12358): 196.96043867527504, (16, 12463): 201.17421795565525, (16, 12465): 201.11761841087855, (16, 12482): 201.9374719697466, (16, 12503): 201.8990881867856, (16, 12506): 202.28995023962455, (16, 12549): 200.63709363267242, (16, 12559): 200.50014002677685, (16, 12569): 201.10661363248653, (16, 12572): 201.38389527731357, (16, 12574): 200.71541212731975, (16, 12576): 200.87927177128526, (16, 12591): 200.3454636246555, (16, 12608): 202.36858316327417, (16, 12696): 198.2800097406218, (16, 12710): 199.8768952028805, (16, 12728): 199.4563500434054, (16, 12766): 136.13678128400286, (16, 12771): 131.05933484147687, (16, 12790): 130.75801328508078, (16, 12795): 130.35225653608185, (16, 12797): 125.2209686807993, (16, 12798): 125.64707341721639, (16, 12811): 128.79565995966675, (16, 12830): 128.16740488431608, (16, 12848): 127.84923907290023, (16, 12850): 127.59661001776932, (16, 12852): 127.75872331099956, (16, 12854): 127.28444597234069, (16, 12859): 128.0974997327111, (16, 12861): 125.97615822847042, (16, 12865): 129.75957270473856, (16, 12866): 129.2608548165991, (16, 12867): 130.4427605793556, (16, 12874): 129.90482449533462, (16, 12875): 130.15679307190382, (16, 12881): 128.97298969443398, (16, 12883): 129.5303204625187, (16, 12885): 130.52733652031594, (16, 12888): 129.09043254677485, (16, 12889): 128.79170612096163, (16, 12892): 130.10436547629513, (16, 12893): 129.28688034117567, (16, 12896): 129.3920519693055, (16, 12906): 130.71293243434738, (16, 13018): 131.3404539727001, (16, 13071): 132.47761037799714, (16, 13131): 124.6131351539407, (16, 13146): 126.63679748839058, (16, 13159): 128.37440443942185, (16, 13193): 123.73044456354248, (16, 13198): 116.85436158241711, (16, 13292): 122.13274350626632, (16, 13296): 121.92396040081913, (16, 13406): 117.06247508809187, (16, 13407): 117.17278458349706, (16, 13417): 118.93888699751109, (16, 13418): 119.78335403360302, (16, 13438): 120.17304693759395, (16, 13442): 119.891963164764, (16, 13443): 119.58344925491893, (16, 13764): 111.93365440464659, (16, 13766): 112.11935736298727, (16, 13771): 112.96892174892427, (16, 13783): 110.05506013947164, (16, 13784): 111.88255643850925, (16, 13792): 114.18075556721811, (16, 13824): 110.13591467636387, (16, 14017): 105.33739986913243, (16, 14870): 58.78668325965089, (16, 14997): 69.45206319736786, (16, 15000): 69.06524743554269, (16, 15003): 68.928574189572, (16, 15006): 71.45427140606866, (16, 15007): 71.69681341856105, (16, 15056): 70.38569067147354, (16, 15063): 69.8753430108387, (16, 15069): 69.3008196729719, (16, 15076): 71.43877266860538, (16, 15086): 71.09662909893885, (16, 15087): 70.1796350566847, (16, 15111): 69.78607509381524, (16, 15116): 69.9626912191887, (16, 15722): 63.72817406492997, (16, 15998): 46.85123740638926, (16, 16073): 141.94042002417189, (16, 16939): 137.88412539599713, (16, 16940): 137.17708528068655, (16, 16951): 138.5831602266269, (16, 16963): 138.50218832329705, (16, 16965): 139.09808723762012, (16, 16969): 139.26706485958042, (16, 16970): 138.60093239633116, (16, 16971): 138.04243294711526, (16, 16973): 138.22241106963986, (16, 16974): 139.54506873005076, (16, 16976): 138.50746198004353, (16, 16978): 138.02307059333148, (16, 16980): 138.53099387813734, (16, 16982): 139.76656506285065, (16, 17045): 176.15895960613366, (16, 17048): 177.00786814967586, (16, 17304): 176.86360211996802, (16, 17305): 176.79899195456372, (16, 17330): 177.10596474641395, (16, 17334): 175.91791430913898, (16, 17343): 177.84035515897918, (16, 17345): 176.2899879890498, (16, 17347): 177.30796440520612, (16, 17351): 174.72754046887303, (16, 17372): 175.97316076008886, (16, 17373): 177.72740310052458, (16, 17377): 177.88352050417035, (16, 17382): 176.82658574485194, (16, 17383): 176.8879139413108, (16, 17389): 176.29673255419863, (16, 17400): 177.3066571291374, (16, 17401): 177.22166504863327, (16, 17402): 177.4080341098124, (16, 17403): 177.54607456354367, (16, 17440): 176.79161161038985, (16, 17455): 177.9208721101497, (16, 17491): 178.31869439026505, (16, 17507): 174.34806656728907, (16, 17509): 174.818335556899, (16, 17590): 174.79597086669315, (16, 17615): 169.00699567951168, (16, 17642): 169.7861236413698, (16, 17643): 169.89255432349373, (16, 17668): 168.88561964258142, (16, 17721): 166.65079784344007, (16, 17754): 171.80643720520624, (16, 17769): 174.0767943886528, (16, 17776): 172.54050434266676, (16, 17804): 174.9335890755079, (16, 17809): 175.50589424215005, (16, 17824): 174.87759932004894, (16, 17837): 174.41482576132472, (16, 17838): 174.70465955254352, (16, 17862): 174.38914259963695, (16, 17866): 175.49538358231322, (16, 17872): 173.84144771061662, (16, 17873): 173.04858247389615, (16, 17881): 174.29933500154328, (16, 17947): 76.27673862402156, (16, 17951): 75.5848287160805, (16, 17953): 75.20994250779665, (16, 17954): 75.09861957560415, (16, 17959): 76.54938465370743, (16, 17963): 76.73218152896594, (16, 18000): 72.72263660004413, (16, 18001): 72.50287640958341, (16, 18111): 75.66718952964557, (16, 18148): 50.265783565331866, (16, 18166): 58.230863401868866, (16, 18189): 68.89243898597971, (16, 18239): 177.86590712934068, (16, 18240): 177.90107924651753, (16, 18245): 177.94118013134909, (16, 18247): 177.8605704048835, (16, 18251): 177.99012251196086, (16, 18256): 178.17944805350658, (16, 18258): 178.05993632772774, (16, 18259): 178.1084294954455, (16, 18260): 178.1958416473583, (16, 18262): 178.3311260940453, (16, 18263): 178.24105178138254, (16, 18264): 178.32530691810973, (16, 18266): 178.41107210343378, (16, 18267): 178.48759719562216, (16, 18268): 178.54087742796088, (16, 18269): 178.69784191230087, (16, 18275): 178.6239780697989, (16, 18285): 178.2801096222699, (16, 18308): 176.6304339027145, (16, 18313): 176.18960335886922, (16, 18314): 176.5220891500757, (16, 18315): 178.5739499883278, (16, 18316): 178.61844568682193, (16, 18317): 178.6953983858843, (16, 18320): 178.68661208310712, (16, 18321): 178.75423180867867, (16, 18322): 178.86407466747704, (16, 18324): 178.87359649136218, (16, 18325): 179.13735997481962, (16, 18326): 179.03651021757582, (16, 18327): 178.8127468083794, (16, 18329): 179.19324434650358, (16, 18330): 179.235682761113, (16, 18331): 179.03162225334418, (16, 18332): 178.85036668123186, (16, 18333): 179.1583638310845, (16, 18336): 178.92651898815905, (16, 18337): 178.98034177196428, (16, 18403): 179.1616231600764, (16, 18432): 177.19290169255308, (16, 18451): 178.53764409290903, (16, 18466): 179.68403773653873, (16, 18481): 178.49352658364475, (16, 18483): 178.53334969156725, (16, 18484): 178.35755665754263, (16, 18485): 177.78734027857428, (16, 18486): 178.0329602711311, (16, 18487): 177.64603483541973, (16, 18489): 178.12926193852485, (16, 18490): 178.35688150480652, (16, 18491): 178.5158091077443, (16, 18492): 177.3403510463903, (16, 18493): 177.92808947731376, (16, 18494): 178.09733347346852, (16, 18495): 178.23238663318807, (16, 18496): 178.09900916775015, (16, 18497): 177.51931716565304, (16, 18498): 177.7621448155506, (16, 18499): 178.02494031375576, (16, 18501): 177.76304587465347, (16, 18502): 177.59019679366125, (16, 18503): 177.50707350391295, (16, 18504): 178.21471004738478, (16, 18506): 177.67122946505344, (16, 18507): 177.48315017012155, (16, 18508): 177.94898555089063, (16, 18509): 177.91382193327877, (16, 18510): 177.45450948816023, (16, 18511): 177.89572157166143, (16, 18512): 177.77483904603912, (16, 18515): 178.17303416467007, (16, 18516): 178.05262329666957, (16, 18517): 177.77592974561196, (16, 18518): 178.2267461698346, (16, 18519): 178.27428902851597, (16, 18520): 177.947919849518, (16, 18522): 179.06161750732974, (16, 18523): 179.05278766768424, (16, 18532): 179.21741664688295, (16, 18535): 178.82994840152898, (16, 18537): 178.61423279306953, (16, 18539): 178.63617193626504, (16, 18540): 178.63677468288134, (16, 18541): 178.72269756076642, (16, 18542): 178.78148125068563, (16, 18543): 178.47132086965055, (16, 18546): 178.54313511094557, (16, 18555): 178.87718446755235, (16, 18556): 178.90762474662307, (16, 18565): 179.1324640179349, (16, 18567): 179.14266123834517, (16, 18568): 178.9978594739203, (16, 18577): 180.32473689291612, (16, 18583): 180.22463295213203, (16, 18605): 180.65081098163466, (16, 18608): 179.07775997177106, (16, 18616): 181.88146579522922, (16, 18618): 182.85122535127326, (16, 18625): 182.8183474752317, (16, 18645): 182.022519074043, (16, 18646): 182.1578175409653, (16, 18653): 180.96851120004607, (16, 18654): 181.8013173095383, (16, 18655): 181.18681158506035, (16, 18666): 185.15298424793428, (16, 18837): 186.10344040011066, (16, 18974): 179.54735782843403, (16, 18999): 180.9847058906713, (16, 19000): 181.31629836428186, (16, 19174): 168.9002875556951, (16, 19342): 176.53681717676116, (16, 19455): 168.93195665086085, (16, 19555): 154.8625254423814, (16, 19564): 157.52983766678344, (16, 19573): 156.4767640241031, (16, 19586): 155.89424047229488, (16, 19605): 155.87415120877262, (16, 19611): 156.5200513645916, (16, 19614): 155.75685387899335, (16, 19641): 164.46859441679857, (16, 19702): 164.8422243272142, (16, 19713): 164.09562994152392, (16, 19731): 149.69607052060047, (16, 19819): 167.47211302632684, (16, 19893): 125.87629432107879, (16, 19899): 128.16125472042663, (16, 19929): 126.84477966524408, (16, 19951): 132.78990850432734, (16, 19962): 126.60669995083998, (16, 19970): 129.3541555654534, (16, 19971): 129.0444600498133, (16, 19972): 128.3011118316005, (16, 19975): 128.3035864431479, (16, 19978): 135.5431232348874, (16, 19987): 135.86879380439674, (16, 19989): 134.1955637465561, (16, 20039): 136.28583933370226, (16, 20043): 137.2960676592193, (16, 20047): 137.02873201460355, (16, 20052): 134.92814362422544, (16, 20054): 134.92597280976355, (16, 20085): 145.48740738706937, (16, 20104): 146.09637036552394, (16, 20132): 142.07462595750192, (16, 20203): 122.45600706035955, (16, 20280): 120.78347010396386, (16, 20285): 120.19940849480396, (16, 20290): 121.2744455166102, (16, 20297): 120.76358424804387, (16, 20309): 133.7124773567611, (16, 20453): 145.11433306905744, (16, 20485): 117.51135320173314, (16, 20520): 116.31986668512847, (16, 20526): 114.70751404913058, (16, 20698): 126.04580734370883, (16, 20868): 128.6579312636727, (16, 21042): 117.80325904452556, (16, 21057): 122.3955870927817, (16, 21066): 119.62367548921583, (16, 21075): 119.5102561342042, (16, 21093): 117.42157373639607, (16, 21098): 119.64325659230582, (16, 21127): 117.79268320439338, (16, 21130): 118.3019741494005, (16, 21144): 118.85469050595901, (16, 21146): 117.4978532601206, (16, 21147): 118.98390156627374, (16, 21148): 119.53439147805022, (16, 21153): 120.37023971148425, (16, 21293): 124.46762701632684, (16, 21426): 129.8620151303453, (16, 21442): 135.8418146904494, (16, 21451): 136.38767538635227, (16, 21466): 132.4861600933551, (16, 21469): 133.04962535553386, (16, 21471): 132.2153715323904, (16, 21473): 132.6002438657046, (16, 21475): 132.16709261355984, (16, 21482): 133.6715161962645, (16, 21484): 133.4141489860494, (16, 21488): 133.1558725424999, (16, 21494): 131.79303359488264, (16, 21498): 132.30777866168273, (16, 21500): 131.20100634615912, (16, 21514): 131.14754018545264, (16, 21537): 130.24082124852845, (16, 21662): 130.7851300351242, (16, 21691): 128.2140747244794, (16, 21757): 126.5188457974715, (16, 21777): 106.79876767629278, (16, 21778): 106.15881336792442, (16, 21779): 106.16043320805984, (16, 21790): 107.90477715865919, (16, 21802): 107.17760182604016, (16, 21824): 107.49868741626645, (16, 21874): 105.89237446989947, (16, 21879): 104.86578567166814, (16, 21983): 111.15631880362155, (16, 22002): 115.80961936265165, (16, 22132): 119.60514217463322, (16, 22261): 25.241282749173124, (16, 22298): 23.77904794620957, (16, 22339): 20.530861088738373, (16, 22508): 30.09824380852186, (16, 22841): 212.55971775243216, (16, 22842): 212.3932374974703, (16, 22874): 210.2130654146455, (16, 22941): 210.95555749660917, (16, 22956): 211.78445171055202, (16, 22960): 212.47974462257454, (16, 22968): 211.1235363212984, (16, 22970): 211.72596928440535, (16, 22974): 210.75028219514437, (16, 22980): 211.9119385320096, (16, 23025): 209.7002158090953, (16, 23028): 209.00740752671024, (16, 23081): 208.38634858000117, (16, 23104): 202.72370243462643, (16, 23147): 198.41996518079392, (16, 23298): 140.82758982693943, (16, 23376): 138.7710408267392, (16, 23381): 136.07171417005807, (16, 23529): 140.95484940619744, (16, 23556): 139.94583275871298, (16, 23718): 140.7923026957025, (16, 24001): 153.34989316366887, (16, 24094): 154.87190816054365, (16, 24129): 156.94121559833923, (16, 24174): 151.74183828785226, (16, 24235): 155.7545444022223, (16, 24259): 158.31545598399507, (16, 24260): 158.07860499310723, (16, 24261): 157.71788162846138, (16, 24305): 160.92123056956447, (16, 24306): 161.20463078871782, (16, 24307): 160.66917023366037, (16, 24308): 160.00382770741857, (16, 24498): 167.8712799222561, (16, 24499): 167.87522249636513, (16, 24500): 167.53815458029356, (16, 24668): 167.17768700351394, (16, 24711): 169.5212158554501, (16, 24756): 170.1791690180016, (16, 24788): 171.07094414651496, (16, 24809): 168.06557566701207, (16, 24813): 169.06269637427764, (16, 24821): 168.76190163715324, (16, 24825): 168.8692396222999, (16, 24832): 167.9542165960535, (16, 24833): 168.3463047762052, (16, 24835): 168.70193749351566, (16, 24837): 169.40751010295043, (16, 24840): 167.85145784223522, (16, 24841): 168.54433260979243, (16, 24844): 167.81240919470932, (16, 24845): 168.3918888565698, (16, 24846): 168.04521967465712, (16, 24849): 168.23172187392754, (16, 24850): 169.11301165841314, (16, 24863): 164.07407423795007, (16, 24866): 164.79584913464333, (16, 24885): 165.43555029321124, (16, 24886): 165.37238053708512, (16, 24889): 167.35399592733611, (16, 24903): 168.14342744077942, (16, 24909): 165.88585091799132, (16, 24999): 197.53945475088398, (16, 25019): 197.16484683647843, (16, 25028): 197.02937452752045, (16, 25137): 118.34734869751458, (16, 25145): 119.1862323821981, (16, 25208): 125.92961645540367, (16, 25233): 124.70523774177143, (16, 25371): 120.51402260762185, (16, 25377): 118.84139480191521, (16, 25828): 80.52219438089493, (16, 25851): 77.0074760004364, (16, 25874): 81.5485926852074, (16, 25898): 82.12940395929189, (16, 25946): 80.06511881901685, (16, 26047): 88.92032604605458, (16, 26066): 110.20657458000217, (16, 26197): 97.65217003054741, (16, 26212): 56.401720402595664, (16, 26253): 53.98572973718849, (16, 26254): 55.024691420190095, (16, 26257): 55.49507999628932, (16, 26258): 54.36239232952268, (16, 26260): 54.972322300826626, (16, 26266): 54.927940584816646, (16, 26267): 55.50676508580177, (16, 26271): 55.421960170585734, (16, 26304): 64.30443445121125, (16, 26305): 64.5189860969059, (16, 26363): 76.53135291810932, (16, 26441): 12.5, (16, 26442): 12.5, (16, 26450): 12.5, (16, 26459): 12.5, (16, 26462): 12.5, (16, 26467): 12.5, (16, 26471): 12.5, (16, 26472): 12.5, (16, 26473): 12.5, (16, 26476): 12.5, (16, 26485): 12.5, (16, 26493): 12.5, (16, 26524): 12.5, (16, 26525): 12.5, (16, 26556): 12.5, (16, 26560): 12.5, (16, 26561): 12.5, (16, 26564): 12.5, (16, 26569): 12.5, (16, 26570): 12.5, (16, 26573): 12.5, (16, 26581): 12.5, (16, 26583): 12.5, (16, 26593): 12.5, (16, 26837): 12.5, (16, 26844): 12.5, (16, 26863): 12.5, (16, 26893): 12.5, (16, 26902): 12.5, (16, 26905): 12.5, (16, 26912): 12.5, (16, 26921): 12.5, (16, 26922): 12.5, (16, 27212): 28.95599005738357, (16, 27218): 29.77294714826136, (16, 27239): 29.305372428795334, (16, 27257): 28.589908609716232, (16, 27274): 29.21068869850049, (16, 27279): 28.70303518994257, (16, 27282): 28.362803192339904, (16, 27283): 29.34384241304591, (16, 27285): 29.114310600552418, (16, 27286): 28.028737103824266, (16, 27290): 28.019294460317635, (16, 27295): 28.49828677122246, (16, 27300): 29.443105301579294, (16, 27344): 26.5778108919946, (16, 27366): 26.51245006872479, (16, 27383): 28.243205343961733, (16, 27398): 29.75917463677294, (16, 27406): 29.691472837407883, (16, 27407): 30.14603163069193, (16, 27426): 32.63440056105015, (16, 27432): 30.52641981129484, (16, 27460): 32.208942195622846, (16, 27523): 19.924813318303805, (16, 27545): 36.691239401191815, (16, 27602): 51.65638060377067, (16, 27606): 52.253815656648534, (16, 27646): 29.194761828626884, (16, 27667): 32.583202844854995, (16, 27672): 32.93737196210303, (16, 27674): 32.240549277664606, (16, 27688): 33.43328312363452, (16, 27692): 33.34557500384365, (16, 27693): 32.78668659628156, (16, 27705): 32.568596492320125, (16, 27712): 32.68741564683719, (16, 27786): 59.97016808208551, (16, 27790): 61.26440564428314, (16, 27791): 61.58392091561277, (16, 27795): 58.823177763724395, (16, 27801): 59.49341384843157, (16, 27813): 60.136097159249395, (16, 27816): 60.127156214545664, (16, 27823): 59.55061787095515, (16, 27830): 60.11181724539595, (16, 27884): 21.44583921569726, (16, 27885): 27.47129864095447, (16, 27896): 23.95334314786043, (16, 27919): 23.93692056742969, (16, 27922): 24.350235594202253, (16, 27930): 22.655237741723347, (16, 27934): 22.68153675062548, (16, 27935): 22.622624256401824, (16, 27948): 43.876294119371735, (16, 27951): 46.26098332587124, (16, 28061): 43.39920047561738, (16, 28290): 72.86238494012993, (16, 28292): 74.23457779144545, (16, 28293): 73.17370211761028, (16, 28295): 73.20806982523423, (16, 28296): 73.01471289128878, (16, 28297): 72.17884288605015, (16, 28302): 72.21767296549243, (16, 28310): 129.96611347994818, (16, 28313): 131.8680834319509, (16, 28372): 129.34120641532454, (16, 28398): 129.5923973349838, (16, 28399): 129.5345102385458, (16, 28400): 129.97032926590416, (16, 28401): 128.49721884668955, (16, 28445): 132.32929117174564, (16, 28475): 125.7815837892734, (16, 28885): 151.92543921925895, (16, 28886): 151.37654477220318, (16, 28915): 151.05054695582336, (16, 28916): 150.9351233983227, (16, 28917): 150.5837269608449, (16, 28921): 152.78522119161747, (16, 28931): 152.50602742991862, (16, 28945): 148.38225562409505, (16, 28982): 149.5812775381975, (16, 29219): 148.2716910658743, (16, 29228): 146.71748558685684, (16, 29246): 155.23166885592735, (16, 29248): 154.47177140004507, (16, 29282): 152.53903972415466, (16, 29290): 156.88591052519752, (16, 29291): 156.29908353479394, (16, 29292): 156.7599711640015, (16, 29293): 155.9738609450214, (16, 29294): 156.3373182504325, (16, 29298): 155.8697866305676, (16, 29299): 155.63658595252247, (16, 29304): 155.26989366135015, (16, 29317): 153.61146614606585, (16, 29323): 153.50220114451184, (16, 29330): 154.2701440065067, (16, 29331): 154.79258351049825, (16, 29344): 147.14441601648807, (16, 29445): 126.48818574437705, (16, 29724): 216.45451980283124, (16, 29738): 216.74749912102303, (16, 29745): 216.14156256083396, (16, 29748): 217.5715648098445, (16, 29750): 218.58144837439926, (16, 29759): 217.01551848825514, (16, 29772): 218.11780783140335, (16, 29781): 217.9132615267001, (16, 29784): 217.18343759363742, (16, 29790): 218.3754282397955, (16, 29811): 218.3079638954986, (16, 29817): 223.63727673253055, (16, 29818): 223.46018561514316, (16, 29929): 215.2536095376179, (16, 30039): 215.61373902031116, (16, 30066): 211.12423485883494, (16, 30116): 203.84748311816892, (16, 30238): 193.25183873167478, (16, 30248): 194.73133163204625, (16, 30260): 194.52970236723326, (16, 30545): 148.50335822877932, (16, 30733): 132.95520777149576, (16, 30756): 124.69257409283344, (16, 30921): 134.2936249803447, (16, 31079): 116.93238018389488, (16, 31149): 110.9557549411711, (16, 31154): 111.64592475538916, (16, 31160): 110.74469917934829, (16, 31163): 111.38439913179057, (16, 31189): 103.14799946436483, (16, 31215): 104.25354077532585, (16, 31259): 106.44112966760781, (16, 31262): 105.4046319093729, (16, 31430): 119.57809402634557, (16, 31568): 106.10675070328041, (16, 31751): 114.58313556866605, (17, 109): 142.14488556759812, (17, 872): 75.48811086841938, (17, 873): 76.17577595949055, (17, 877): 75.71857036129454, (17, 879): 75.80187397352714, (17, 884): 74.66564862739884, (17, 889): 75.19359418400708, (17, 891): 74.48961563944401, (17, 892): 76.37993827093842, (17, 894): 76.37268861640051, (17, 896): 76.03982340730585, (17, 903): 75.51958014589607, (17, 909): 75.01044024965778, (17, 910): 75.47273469135955, (17, 912): 74.98022801043929, (17, 913): 74.3680215429211, (17, 916): 74.39365710333625, (17, 926): 75.9465712334887, (17, 927): 75.76279982964489, (17, 948): 74.27157951746423, (17, 961): 75.47651926439555, (17, 962): 75.68595446812253, (17, 963): 75.87892818345705, (17, 967): 75.89270224860007, (17, 974): 75.06491228354685, (17, 998): 76.00843949487415, (17, 1014): 94.01858721875864, (17, 1086): 79.91051413899257, (17, 1087): 80.64565112105646, (17, 1089): 79.65097836896796, (17, 1090): 79.84269005052502, (17, 1092): 80.73300128521923, (17, 1097): 79.89279416521471, (17, 1107): 81.68826902988211, (17, 1387): 99.00715669904609, (17, 1554): 107.0660161796488, (17, 1827): 108.02200837254034, (17, 1828): 108.15178011058576, (17, 1829): 108.25292565532382, (17, 1830): 107.93264398411061, (17, 1831): 108.04103315553247, (17, 1832): 107.96835379128329, (17, 1833): 108.01050431553843, (17, 1836): 107.94985576406012, (17, 1841): 108.44164111867576, (17, 1843): 108.21570916833642, (17, 1844): 108.2848027781732, (17, 1845): 107.988072012741, (17, 1847): 107.2124495699821, (17, 1848): 107.49989491461479, (17, 1849): 108.8201903665024, (17, 1850): 108.9909029393212, (17, 1851): 107.63504925763492, (17, 1852): 107.58386280156924, (17, 1854): 107.7794170069904, (17, 1856): 107.07268266048779, (17, 1857): 107.43955121096685, (17, 1858): 108.73857949948221, (17, 1861): 108.17024018922041, (17, 1866): 106.99061583762588, (17, 1867): 108.51937551239978, (17, 1868): 108.39930426022569, (17, 1870): 108.16674476184075, (17, 1871): 108.54121967646304, (17, 1875): 107.81396632751209, (17, 1880): 107.32070760498318, (17, 1882): 107.30127501206674, (17, 1883): 109.08473369414125, (17, 1889): 107.59893052250149, (17, 1893): 108.3932414752204, (17, 1894): 108.20623932583673, (17, 1899): 107.46696424209311, (17, 1900): 107.64728051205428, (17, 1902): 108.75614998586676, (17, 1905): 108.97664938429378, (17, 1907): 107.77679526896826, (17, 1910): 107.97030372875528, (17, 1917): 109.79449045486759, (17, 1920): 107.86394598991674, (17, 1935): 109.16009733979782, (17, 1937): 109.36477640347145, (17, 1946): 107.18068768458245, (17, 1949): 107.48014281459422, (17, 1950): 106.37055560164004, (17, 1951): 106.86222017984007, (17, 1952): 106.9929304985438, (17, 1953): 107.319378163481, (17, 1954): 106.97703539056366, (17, 1958): 107.32073578209517, (17, 1960): 107.71178154272972, (17, 1968): 107.86697565991375, (17, 1969): 109.3641979692687, (17, 1974): 108.95875325082133, (17, 1975): 108.90476665896337, (17, 1979): 108.37101600700628, (17, 1980): 108.16940193452615, (17, 1981): 108.44977718775858, (17, 1985): 108.64478698570979, (17, 1994): 105.67345494087488, (17, 2011): 107.2424003554579, (17, 2019): 109.28167470153643, (17, 2020): 109.00941592675849, (17, 2029): 107.85071274267855, (17, 2030): 108.82302373223006, (17, 2032): 107.59591396206241, (17, 2033): 108.27524823186764, (17, 2034): 108.20108773447038, (17, 2036): 106.8066114595425, (17, 2037): 107.17230399034894, (17, 2038): 107.56682247547984, (17, 2042): 110.90977920371034, (17, 2050): 108.21948968463371, (17, 2051): 108.10103162186527, (17, 2053): 108.2203011901014, (17, 2054): 108.51302382860933, (17, 2066): 107.9051251896265, (17, 2067): 107.94327019351881, (17, 2071): 105.15886329114718, (17, 2072): 105.76801411076102, (17, 2073): 104.45963805821889, (17, 2074): 104.33345244438816, (17, 2080): 103.27444236574911, (17, 2082): 106.07933079889732, (17, 2083): 106.398971036953, (17, 2089): 105.84384846483808, (17, 2090): 106.15539643682791, (17, 2092): 105.83347606230478, (17, 2098): 103.7343735724696, (17, 2099): 104.00937101591158, (17, 2101): 103.60585632718727, (17, 2102): 105.2110911096459, (17, 2103): 104.67807570853934, (17, 2104): 104.35403195206746, (17, 2106): 106.56439598308148, (17, 2112): 103.75450295070453, (17, 2113): 105.39714130391594, (17, 2114): 105.6667266282727, (17, 2117): 106.74746093497946, (17, 2123): 107.69827131980013, (17, 2124): 108.02459694668454, (17, 2134): 106.83731375714237, (17, 2138): 107.90041721668197, (17, 2141): 107.02910826599954, (17, 2148): 106.55790245898774, (17, 2150): 106.18707492126295, (17, 2151): 106.45804428069815, (17, 2152): 105.93905323184264, (17, 2153): 106.75536407769701, (17, 2154): 105.45522051113133, (17, 2155): 105.14355737489316, (17, 2156): 105.00203753299583, (17, 2157): 104.79409552767048, (17, 2160): 107.89058803035164, (17, 2161): 105.78497574229598, (17, 2162): 106.47228816247191, (17, 2163): 106.04076413838378, (17, 2164): 105.95619945512799, (17, 2168): 105.82076610920198, (17, 2172): 105.70077295903911, (17, 2174): 106.29518245927189, (17, 2178): 105.84857079075626, (17, 2179): 105.60251409988938, (17, 2183): 107.76402759236687, (17, 2185): 107.72415002820804, (17, 2186): 107.49537321126486, (17, 2190): 108.0587749236522, (17, 2192): 107.62470979423398, (17, 2193): 107.88955464118963, (17, 2194): 107.44761093091581, (17, 2195): 107.25327030189038, (17, 2197): 107.65767330201372, (17, 2205): 106.85795036123888, (17, 2207): 105.85760878749097, (17, 2208): 106.39213131713866, (17, 2212): 108.30745646977955, (17, 2214): 97.06917227512568, (17, 2225): 97.83554600318642, (17, 2231): 98.54783707918908, (17, 2278): 101.75051899587653, (17, 2284): 102.55011688259873, (17, 2285): 102.35259122542698, (17, 2291): 100.03259339993716, (17, 2292): 100.74300096123687, (17, 2307): 101.91353334764538, (17, 2313): 99.6580365414325, (17, 2317): 100.25377030780024, (17, 2319): 101.02114979969963, (17, 2321): 101.37658961665882, (17, 2323): 101.4634749423753, (17, 2326): 103.4120269590313, (17, 2327): 102.99914208882828, (17, 2329): 102.70181585722324, (17, 2330): 102.32748505849891, (17, 2332): 102.93820776009618, (17, 2344): 102.10336371968694, (17, 2346): 101.9768127126279, (17, 2361): 102.7680687217395, (17, 2368): 107.00630925440734, (17, 2374): 107.37935485446795, (17, 2375): 107.58357786841096, (17, 2377): 106.08065565820245, (17, 2378): 107.82470580600273, (17, 2379): 107.76098908986913, (17, 2380): 107.9906370156677, (17, 2383): 106.56758857264634, (17, 2385): 106.84903416727137, (17, 2395): 106.97398327973826, (17, 2397): 107.52640410528159, (17, 2398): 105.59125415133211, (17, 2399): 106.20674679691861, (17, 2400): 106.08242358587131, (17, 2402): 106.68155944959223, (17, 2403): 107.02664258268065, (17, 2404): 107.15808532650492, (17, 2405): 106.2885452346747, (17, 2407): 107.05907832455291, (17, 2408): 107.4194324493387, (17, 2409): 106.56863283644195, (17, 2411): 106.85410526346092, (17, 2412): 106.8265611855466, (17, 2413): 107.08725140549208, (17, 2414): 106.60264374955644, (17, 2422): 106.69027527207844, (17, 2424): 106.96151337887136, (17, 2426): 107.0712008530294, (17, 2433): 106.35855613230416, (17, 2436): 106.07511804616679, (17, 2437): 104.08405012212253, (17, 2440): 104.55313825576698, (17, 2445): 112.82178474421877, (17, 2447): 111.76400328869087, (17, 2454): 112.83060414691481, (17, 2455): 112.95280453959143, (17, 2460): 109.56047756615447, (17, 2461): 109.96453232632446, (17, 2471): 116.28359344407384, (17, 2492): 107.67770588643803, (17, 2511): 104.37840061976313, (17, 2523): 106.05156815952527, (17, 2525): 105.48399001681663, (17, 2535): 107.04655633735082, (17, 2537): 106.26691972901911, (17, 2538): 106.84964689741416, (17, 2539): 106.41847041198996, (17, 2540): 107.39469190018531, (17, 2542): 107.88454867557876, (17, 2559): 119.11044462099821, (17, 2575): 117.87756253712186, (17, 2599): 102.41708313472698, (17, 2600): 105.80578557802235, (17, 2607): 104.09751159901687, (17, 2627): 106.18296377140945, (17, 2647): 108.20325979570076, (17, 2674): 107.19269349412149, (17, 2681): 106.88607753514556, (17, 2683): 107.89076615323097, (17, 2686): 106.76040906112897, (17, 2689): 120.04048193058291, (17, 2690): 120.10476596346486, (17, 2713): 122.8764296394329, (17, 2714): 123.15649398767137, (17, 2715): 123.48423102252734, (17, 2739): 123.17687980113463, (17, 2740): 120.97789671800322, (17, 2741): 121.13365257427955, (17, 2749): 122.78631236195812, (17, 2750): 122.86708322099872, (17, 2752): 123.09125361627993, (17, 2755): 123.36395693622393, (17, 2758): 123.30661403871204, (17, 2759): 123.2978684467708, (17, 2769): 122.89255961134944, (17, 2771): 121.53691365278856, (17, 2779): 121.77182210239425, (17, 2784): 118.14531769611109, (17, 2800): 118.99895103299316, (17, 2802): 120.40141172601402, (17, 2803): 120.26134767392914, (17, 2804): 120.03601601830147, (17, 2805): 120.72789422179711, (17, 2807): 120.69000658665607, (17, 2809): 120.60741859061609, (17, 2812): 118.45333190714648, (17, 2814): 120.63436782796188, (17, 2817): 120.94050207073006, (17, 2819): 120.69326101183864, (17, 2823): 118.82946436969475, (17, 2832): 121.16207373666239, (17, 2836): 119.67889295621355, (17, 2839): 120.66835301043066, (17, 2841): 120.88848044191721, (17, 2843): 120.7374482180852, (17, 2846): 120.052201676031, (17, 2849): 121.42596931680195, (17, 2852): 121.07658566054788, (17, 2853): 121.58812323805395, (17, 2876): 121.83900611828075, (17, 2877): 123.04534762343002, (17, 2885): 123.66019868499426, (17, 2918): 120.77675383709465, (17, 2921): 121.30212967748729, (17, 2925): 118.82384624267493, (17, 2926): 118.0041115115865, (17, 2930): 119.93873500858594, (17, 2931): 119.06329213358329, (17, 2938): 120.80374193324576, (17, 2940): 122.20984968116606, (17, 2947): 120.4505773177581, (17, 2949): 119.87556720083364, (17, 2950): 120.12529772325713, (17, 2952): 119.87320141098805, (17, 2958): 119.81558866045903, (17, 2959): 120.03744167999342, (17, 2960): 120.60715009139815, (17, 2961): 120.34563629938873, (17, 2963): 119.61335264564443, (17, 2968): 119.78705250853544, (17, 2976): 119.53374821779562, (17, 2981): 114.9198545930101, (17, 2982): 114.82350186691255, (17, 2984): 114.58382516320276, (17, 3003): 114.19585215854761, (17, 3046): 110.57893227100138, (17, 3050): 113.26295789460781, (17, 3051): 113.4492973585943, (17, 3053): 112.91063331407749, (17, 3069): 116.04443858161157, (17, 3071): 112.71700630963723, (17, 3080): 123.77464216089558, (17, 3199): 113.72819577866375, (17, 3200): 113.19398384841993, (17, 3205): 116.72783259549273, (17, 3209): 113.50449775323736, (17, 3215): 113.1923571649644, (17, 3217): 112.48917903238949, (17, 3249): 113.21789599045644, (17, 3263): 118.5198052627903, (17, 3289): 114.80014528596963, (17, 3301): 115.05770793509616, (17, 3302): 114.77068884383463, (17, 3307): 114.44496683233322, (17, 3310): 115.36089763142512, (17, 3391): 118.77738623937113, (17, 3509): 12.5, (17, 3510): 12.5, (17, 3511): 12.5, (17, 3512): 12.5, (17, 3514): 12.5, (17, 3519): 12.5, (17, 3536): 12.5, (17, 3545): 12.5, (17, 3548): 12.5, (17, 3572): 12.5, (17, 3581): 12.5, (17, 3583): 12.5, (17, 3601): 12.5, (17, 3656): 12.5, (17, 3669): 12.5, (17, 3670): 12.5, (17, 3695): 12.5, (17, 3696): 12.5, (17, 3782): 12.5, (17, 3792): 12.5, (17, 3989): 217.23954528025837, (17, 4008): 219.84736125130743, (17, 4031): 219.38561354038708, (17, 4045): 218.73851602017731, (17, 4144): 219.15385652626037, (17, 4145): 216.83325748309727, (17, 4164): 218.2166506409338, (17, 4168): 217.54204582937643, (17, 4173): 217.44505626127184, (17, 4181): 215.85514968305236, (17, 4228): 214.03845545744505, (17, 4248): 213.81142419257523, (17, 4254): 200.85407104667448, (17, 4260): 200.7750533735992, (17, 4262): 201.77570494092598, (17, 4273): 201.4922581387683, (17, 4319): 193.48915784928698, (17, 4326): 193.175807474182, (17, 4328): 193.25560414048275, (17, 4334): 193.88810163550858, (17, 4335): 193.70263014851906, (17, 4372): 190.24892519875718, (17, 4413): 198.7631180116063, (17, 4434): 189.9049003480212, (17, 4447): 191.07656923034511, (17, 4452): 190.01744538728232, (17, 4463): 172.20790669146226, (17, 4465): 172.8170023080938, (17, 4619): 199.59396627089848, (17, 4645): 201.52273818775038, (17, 4657): 201.1983315687078, (17, 4666): 200.43763271151474, (17, 4676): 201.7664452127509, (17, 4678): 202.07481894156956, (17, 4689): 201.13939267318258, (17, 4704): 207.73058771609598, (17, 4726): 222.89550011018656, (17, 4727): 222.61173245210293, (17, 4730): 222.06507755925392, (17, 4731): 222.19798881528223, (17, 4734): 222.6456752361095, (17, 4735): 222.35619028543317, (17, 4736): 222.47365914968313, (17, 4737): 221.97225902843456, (17, 4738): 222.0213404706333, (17, 4756): 222.29395204801, (17, 4760): 220.97432243456248, (17, 4761): 221.17690276436448, (17, 4762): 220.56120995807655, (17, 4765): 221.10129398397314, (17, 4773): 223.4744220108035, (17, 4774): 223.18040591128255, (17, 4790): 223.29197163230538, (17, 4795): 223.05436892342044, (17, 4799): 223.2815770749912, (17, 4801): 223.82085344549762, (17, 4804): 223.20215114410598, (17, 4805): 223.0064365673293, (17, 4806): 223.01263541665375, (17, 4815): 222.70481182065222, (17, 4816): 223.43467912214436, (17, 4817): 223.52889459071622, (17, 4826): 223.11940332856477, (17, 4830): 222.69598590289817, (17, 4839): 221.79748650445367, (17, 4840): 222.03027157447178, (17, 4841): 221.41664324433194, (17, 4846): 221.22813927278048, (17, 4848): 221.12319872912246, (17, 4850): 221.37390234256418, (17, 4871): 218.2764412097122, (17, 4883): 220.71469480163518, (17, 4900): 219.51833276814847, (17, 4901): 219.1333757542358, (17, 4917): 198.63946094994424, (17, 4931): 196.51964117664716, (17, 4944): 198.91262437043864, (17, 4956): 196.875405330563, (17, 4958): 196.749192248708, (17, 4959): 196.30237649317397, (17, 4961): 197.33126785868873, (17, 4966): 196.31959371336868, (17, 5207): 193.96389153973894, (17, 5272): 156.19139607578978, (17, 5283): 156.92152158232258, (17, 5287): 157.8804841215214, (17, 5289): 158.19431148840386, (17, 5293): 156.53575844185605, (17, 5295): 158.60700821483823, (17, 5296): 158.46273140411114, (17, 5298): 158.36654304865303, (17, 5303): 158.87147003445793, (17, 5305): 155.51285826031116, (17, 5306): 154.7568761614366, (17, 5307): 155.1177449382317, (17, 5308): 155.81210763338947, (17, 5313): 155.9417168139175, (17, 5314): 156.45710166221642, (17, 5317): 155.7344489339408, (17, 5319): 158.1253675687458, (17, 5324): 157.8036066107899, (17, 5326): 157.60509184784502, (17, 5348): 154.47683525009768, (17, 5351): 154.8537241927033, (17, 5399): 158.4345622630062, (17, 5413): 155.5389828528403, (17, 5422): 158.95879137850096, (17, 5445): 157.2026961928747, (17, 5448): 156.49232932032388, (17, 5456): 156.19382151163768, (17, 5467): 156.82015060775706, (17, 5624): 149.48080831593694, (17, 5671): 174.21809721679554, (17, 5672): 173.2643404849601, (17, 5797): 185.7434574641433, (17, 5871): 167.4993869621441, (17, 5976): 158.93641963810813, (17, 6118): 68.77677957520774, (17, 6248): 83.69180180530172, (17, 6345): 116.96763178093393, (17, 6352): 114.73571480106024, (17, 6354): 117.47462876287152, (17, 6359): 117.98897146258773, (17, 6376): 115.2844664665204, (17, 6378): 117.21705690801066, (17, 6381): 117.85681078153867, (17, 6383): 116.46361856196624, (17, 6396): 117.91491432454794, (17, 6399): 117.08598067746932, (17, 6408): 114.73885425971258, (17, 6409): 115.60226434124645, (17, 6419): 111.68659371542333, (17, 6422): 114.87927359663159, (17, 6423): 114.68772246092487, (17, 6424): 117.05217927810392, (17, 6439): 116.56438715029009, (17, 6464): 115.88628922838903, (17, 6465): 115.71932029789788, (17, 6469): 116.1295340678712, (17, 6470): 116.02290168946674, (17, 6472): 118.77646254641846, (17, 6480): 118.01759318564653, (17, 6486): 119.11762925810045, (17, 6497): 118.72844108853971, (17, 6503): 115.74440392123553, (17, 6508): 116.0532607895701, (17, 6509): 116.4255793467856, (17, 6521): 118.18590738167686, (17, 6544): 117.88717642469581, (17, 6552): 114.96827693352398, (17, 6553): 114.59898897385955, (17, 6554): 114.22534308616575, (17, 6578): 115.60812179267708, (17, 6582): 115.1832059383063, (17, 6601): 115.7427343031132, (17, 6609): 118.84736641921509, (17, 6610): 118.9162255757034, (17, 6611): 119.07977773466112, (17, 6614): 118.9474056940858, (17, 6615): 118.98097301753333, (17, 6616): 119.24162386357378, (17, 6617): 119.11583543232429, (17, 6618): 119.53897446964467, (17, 6619): 118.66368026827814, (17, 6620): 119.19570828247377, (17, 6621): 118.87447974327553, (17, 6622): 118.98404467799308, (17, 6623): 118.84953413493278, (17, 6624): 118.51347730908842, (17, 6625): 118.48599641048858, (17, 6626): 118.67274117456374, (17, 6627): 118.92473206559232, (17, 6628): 119.07851406749333, (17, 6629): 118.53188201690573, (17, 6630): 118.31443367987629, (17, 6632): 118.53035842618534, (17, 6634): 117.94117429634021, (17, 6635): 118.79165017898264, (17, 6636): 119.24023277758332, (17, 6637): 118.09956069006562, (17, 6638): 118.29526865887617, (17, 6639): 118.92086275177965, (17, 6640): 118.3774507262005, (17, 6641): 118.8258706285985, (17, 6642): 118.26363763971783, (17, 6643): 118.68144087351214, (17, 6645): 118.68001064657454, (17, 6646): 119.46865012800889, (17, 6647): 118.37851576374156, (17, 6653): 118.98526694021723, (17, 6655): 118.94428405252262, (17, 6658): 117.89490489264571, (17, 6662): 118.20499865672714, (17, 6819): 99.74196339996415, (17, 6996): 105.51171462767803, (17, 7059): 109.75205531118026, (17, 7187): 103.65769350561769, (17, 7304): 93.62241521483044, (17, 7528): 105.3632584680891, (17, 7720): 130.3525576285106, (17, 7793): 129.93673800404972, (17, 7807): 130.24357326805188, (17, 7808): 129.84251984990283, (17, 7831): 120.78795077140254, (17, 7850): 124.99256988814429, (17, 7852): 124.14566505481646, (17, 8012): 129.09992469053623, (17, 8125): 133.82368186237943, (17, 8208): 138.15585657568437, (17, 8392): 123.51695616155185, (17, 8651): 79.52740344939947, (17, 9088): 99.61947116378947, (17, 9443): 70.59617347676263, (17, 9444): 71.27141910505468, (17, 9828): 55.94741221445031, (17, 9868): 51.83449749300536, (17, 10180): 134.3754485226917, (17, 10256): 145.4022214339831, (17, 10276): 140.07963747486278, (17, 10378): 140.8427176129655, (17, 10676): 132.25744563375477, (17, 10714): 125.6445557461445, (17, 10730): 125.60687415200508, (17, 10862): 139.15562681695187, (17, 10881): 140.84298087399134, (17, 10883): 140.69546454580993, (17, 10885): 138.78274121349205, (17, 10891): 140.47078699522044, (17, 10909): 140.22785210209793, (17, 10911): 140.36852707637536, (17, 10913): 140.00980496446917, (17, 10915): 139.9429500213348, (17, 10919): 140.1368474189301, (17, 11037): 130.18148535336638, (17, 11039): 125.37130032753191, (17, 11516): 242.3078028515762, (17, 11856): 194.15072462957863, (17, 11857): 193.83492976595872, (17, 11861): 194.0092472006998, (17, 11881): 193.44863584929865, (17, 11902): 191.58045294097366, (17, 11911): 191.1643631569141, (17, 11914): 191.45775433426627, (17, 11922): 192.87307819505003, (17, 11924): 193.2933965604614, (17, 11926): 192.75066149524105, (17, 11950): 193.72743550462727, (17, 11963): 195.49764351297796, (17, 11983): 194.15367518782026, (17, 11985): 196.39307710972906, (17, 12009): 195.9196392801744, (17, 12010): 194.69615137337604, (17, 12018): 194.88555874261874, (17, 12020): 195.24475560123355, (17, 12021): 195.43842072568128, (17, 12024): 196.63750358445324, (17, 12025): 196.25848508702853, (17, 12027): 195.9680469882913, (17, 12031): 194.48703071799181, (17, 12032): 194.92463703023293, (17, 12035): 195.8100721401438, (17, 12041): 196.62007359620102, (17, 12045): 179.82307735599912, (17, 12145): 187.3684852909741, (17, 12275): 217.82736542888756, (17, 12294): 214.49199016041706, (17, 12358): 224.29879051367413, (17, 12463): 228.0294206110587, (17, 12465): 227.90866567939057, (17, 12482): 229.68593769095105, (17, 12503): 229.42835060455536, (17, 12506): 229.88936408344793, (17, 12549): 228.99964005234995, (17, 12559): 228.62595447538058, (17, 12569): 228.96542729857333, (17, 12572): 229.3143418394228, (17, 12574): 228.59708769509265, (17, 12576): 229.41384021418406, (17, 12591): 229.39493419088643, (17, 12608): 232.2471952918128, (17, 12696): 227.79674861331347, (17, 12710): 230.5139024007298, (17, 12728): 229.1367672663984, (17, 12766): 153.78554914946307, (17, 12771): 150.50294209645816, (17, 12790): 150.04020054539623, (17, 12795): 148.95960619822958, (17, 12797): 144.6662050512448, (17, 12798): 145.2742787544791, (17, 12811): 148.75945420398935, (17, 12830): 147.55968569458696, (17, 12848): 148.23355119429877, (17, 12850): 148.57053639371338, (17, 12852): 147.41271385200105, (17, 12854): 146.87726095732037, (17, 12859): 148.78454205683832, (17, 12861): 145.88202431248158, (17, 12865): 149.38923640467024, (17, 12866): 149.13183688993243, (17, 12867): 150.18826562734384, (17, 12874): 149.67319185997044, (17, 12875): 150.08612471965515, (17, 12881): 148.4039409745491, (17, 12883): 149.0683838529061, (17, 12885): 150.43368837075064, (17, 12888): 148.77308649823544, (17, 12889): 148.6354586579946, (17, 12892): 149.7812939831155, (17, 12893): 148.78524083578083, (17, 12896): 149.11680723992194, (17, 12906): 149.65933352537283, (17, 13018): 144.74578498619695, (17, 13071): 144.82359213289664, (17, 13131): 140.51763138236078, (17, 13146): 144.07368196907186, (17, 13159): 139.22479547783087, (17, 13193): 139.83818979322777, (17, 13198): 133.69578059758376, (17, 13292): 140.8388720421282, (17, 13296): 142.9816182904904, (17, 13406): 129.79164933130667, (17, 13407): 129.59230730500576, (17, 13417): 129.18823317955687, (17, 13418): 129.87268440049283, (17, 13438): 132.52659841525397, (17, 13442): 133.0499516060595, (17, 13443): 132.52944124458244, (17, 13764): 91.08136762602393, (17, 13766): 91.69889955515261, (17, 13771): 91.43490853436403, (17, 13783): 90.01986699576508, (17, 13784): 92.23285909166303, (17, 13792): 90.79089062262085, (17, 13824): 89.65765348651718, (17, 14017): 91.7386667400905, (17, 14870): 137.36295684773165, (17, 14997): 100.73552358663284, (17, 15000): 100.96669532305297, (17, 15003): 101.58802487066369, (17, 15006): 101.88893476547075, (17, 15007): 102.36330772240615, (17, 15056): 102.7816261635571, (17, 15063): 102.47052765844289, (17, 15069): 102.51099953151434, (17, 15076): 102.5455461384762, (17, 15086): 100.90886406599228, (17, 15087): 100.63017543162499, (17, 15111): 99.09846158158322, (17, 15116): 99.9934410783734, (17, 15722): 87.73000099703152, (17, 15998): 85.12835516708755, (17, 16073): 58.97517072578006, (17, 16939): 78.36391168985155, (17, 16940): 77.75168187342548, (17, 16951): 78.23082144177248, (17, 16963): 78.34233423564882, (17, 16965): 79.18667825453916, (17, 16969): 78.87196362628102, (17, 16970): 78.68985792367242, (17, 16971): 77.93676622848893, (17, 16973): 77.8097129771286, (17, 16974): 79.45266737764199, (17, 16976): 78.79817311821209, (17, 16978): 78.27562925832191, (17, 16980): 79.14530867774222, (17, 16982): 79.36910707362097, (17, 17045): 101.85641837287098, (17, 17048): 102.78894406994702, (17, 17304): 210.38514937828924, (17, 17305): 209.77594095072672, (17, 17330): 210.25898997194284, (17, 17334): 209.51889376352537, (17, 17343): 210.8986400041404, (17, 17345): 209.32779893494074, (17, 17347): 210.09434247952723, (17, 17351): 208.3059240986258, (17, 17372): 209.3593141350132, (17, 17373): 210.87016726640127, (17, 17377): 210.96339069536916, (17, 17382): 209.94599231613674, (17, 17383): 210.18800885923093, (17, 17389): 209.57477943827155, (17, 17400): 210.63631448550012, (17, 17401): 210.64107560145254, (17, 17402): 210.68127493674538, (17, 17403): 210.76993680835656, (17, 17440): 209.21908035686118, (17, 17455): 210.616735341031, (17, 17491): 210.59793372378206, (17, 17507): 209.27614210496768, (17, 17509): 209.88892060236, (17, 17590): 207.74550860386077, (17, 17615): 205.60830165184555, (17, 17642): 206.09870410453075, (17, 17643): 205.9852934269617, (17, 17668): 205.62530052987498, (17, 17721): 204.64071342593155, (17, 17754): 210.1468959283307, (17, 17769): 209.6499158825687, (17, 17776): 207.07264192154813, (17, 17804): 210.610518168374, (17, 17809): 211.1870740425978, (17, 17824): 210.9140661469421, (17, 17837): 208.76186717961124, (17, 17838): 208.733276735673, (17, 17862): 208.26088549686696, (17, 17866): 209.53139960307013, (17, 17872): 207.90236171063043, (17, 17873): 206.91116609062541, (17, 17881): 208.41839214750368, (17, 17947): 43.88411897191282, (17, 17951): 42.65725320767974, (17, 17953): 42.76122688308225, (17, 17954): 43.06713247101944, (17, 17959): 43.059854344109205, (17, 17963): 42.04913719678131, (17, 18000): 36.951354682791234, (17, 18001): 37.643840619230545, (17, 18111): 67.83963469863303, (17, 18148): 49.50527118485943, (17, 18166): 57.07882930810701, (17, 18189): 61.786421880840756, (17, 18239): 211.22307399860918, (17, 18240): 211.19502942429656, (17, 18245): 211.26606456716448, (17, 18247): 211.1172335305248, (17, 18251): 211.23812562091442, (17, 18256): 211.3445134022159, (17, 18258): 211.1874617309044, (17, 18259): 211.2021474224515, (17, 18260): 211.24243557623691, (17, 18262): 211.33463714389117, (17, 18263): 211.37045080278858, (17, 18264): 211.41187470330044, (17, 18266): 211.3587348255112, (17, 18267): 211.40227927431087, (17, 18268): 211.41578934670156, (17, 18269): 211.50034964321577, (17, 18275): 211.46035599061767, (17, 18285): 211.40613713336998, (17, 18308): 210.5170811663511, (17, 18313): 210.15609540407004, (17, 18314): 210.25439322564262, (17, 18315): 211.55452399175525, (17, 18316): 211.51845246325544, (17, 18317): 211.55621488260556, (17, 18320): 211.63283963210836, (17, 18321): 211.6407967310248, (17, 18322): 211.70607681755942, (17, 18324): 211.799709224016, (17, 18325): 212.0421295235821, (17, 18326): 211.95311359025587, (17, 18327): 211.5671071291963, (17, 18329): 212.1826497939175, (17, 18330): 211.97336469463164, (17, 18331): 211.8250142486185, (17, 18332): 211.65761034077917, (17, 18333): 211.9732527940776, (17, 18336): 211.8795513616645, (17, 18337): 211.9799906084972, (17, 18403): 211.6981512032866, (17, 18432): 207.57029883386053, (17, 18451): 210.36351405104318, (17, 18466): 213.1591138380429, (17, 18481): 211.69240845933086, (17, 18483): 211.67251054224002, (17, 18484): 211.55432096783187, (17, 18485): 211.21855102033834, (17, 18486): 211.646198688567, (17, 18487): 211.35983337145638, (17, 18489): 211.5424531930499, (17, 18490): 211.90525260106554, (17, 18491): 212.05130548410574, (17, 18492): 211.0314165234581, (17, 18493): 211.6176381809635, (17, 18494): 211.4672087234841, (17, 18495): 211.799357881694, (17, 18496): 211.63020806308185, (17, 18497): 211.31197583634398, (17, 18498): 211.30358271866976, (17, 18499): 211.52368847681555, (17, 18501): 211.39892438466387, (17, 18502): 211.26035039524166, (17, 18503): 211.13023386736558, (17, 18504): 211.66652753858418, (17, 18506): 211.47604866851128, (17, 18507): 211.35499558766585, (17, 18508): 211.51198413130558, (17, 18509): 211.533317453137, (17, 18510): 211.16111685970947, (17, 18511): 211.69990390631042, (17, 18512): 211.49642226038344, (17, 18515): 211.7076138108359, (17, 18516): 211.7827762277613, (17, 18517): 211.63560044185, (17, 18518): 211.88212905400798, (17, 18519): 211.68577254290204, (17, 18520): 211.44698067019172, (17, 18522): 212.2486061096002, (17, 18523): 212.3008891158644, (17, 18532): 212.5292697588516, (17, 18535): 212.07649485374762, (17, 18537): 211.824402854377, (17, 18539): 211.8881205586876, (17, 18540): 211.9290935368681, (17, 18541): 212.06278780390042, (17, 18542): 212.1456664162135, (17, 18543): 211.74254218786848, (17, 18546): 211.96971189304531, (17, 18555): 212.36681974998618, (17, 18556): 212.45333739771812, (17, 18565): 212.52815500759968, (17, 18567): 212.68516381469635, (17, 18568): 212.4511199384178, (17, 18577): 213.99529694835002, (17, 18583): 213.67901345375023, (17, 18605): 213.93504642727743, (17, 18608): 212.901288525638, (17, 18616): 215.38085421429128, (17, 18618): 216.6470856873749, (17, 18625): 216.07632198102954, (17, 18645): 214.9280447270354, (17, 18646): 215.26094497788674, (17, 18653): 214.37842323038936, (17, 18654): 215.37400115760107, (17, 18655): 214.75052347583014, (17, 18666): 218.49434138168684, (17, 18837): 211.97960759190286, (17, 18974): 209.87174527339283, (17, 18999): 210.65975001603454, (17, 19000): 211.02609724767868, (17, 19174): 192.51197443324523, (17, 19342): 199.65923999964994, (17, 19455): 195.99831782642906, (17, 19555): 177.58529660157126, (17, 19564): 178.47193501010955, (17, 19573): 177.7302001544539, (17, 19586): 177.41182037127717, (17, 19605): 177.73466482199447, (17, 19611): 178.24182268992675, (17, 19614): 178.06452182545877, (17, 19641): 186.77767527243273, (17, 19702): 186.56789859591342, (17, 19713): 185.9413648893226, (17, 19731): 174.92847264399836, (17, 19819): 193.0681009582248, (17, 19893): 177.3486822396594, (17, 19899): 181.5476607937604, (17, 19929): 178.42232645771838, (17, 19951): 186.67813125206723, (17, 19962): 179.14994944869687, (17, 19970): 180.85820110018898, (17, 19971): 180.91921335973817, (17, 19972): 180.2413532374724, (17, 19975): 179.8977259534772, (17, 19978): 188.33187079509963, (17, 19987): 188.46254515630503, (17, 19989): 186.19131253476868, (17, 20039): 188.87519765869826, (17, 20043): 189.81041802640704, (17, 20047): 189.07233817474, (17, 20052): 186.57117788768198, (17, 20054): 186.77514405003782, (17, 20085): 198.08849255400517, (17, 20104): 198.79798949070369, (17, 20132): 194.46354880920995, (17, 20203): 177.13181891404236, (17, 20280): 176.2775681012751, (17, 20285): 176.07574011973233, (17, 20290): 176.66107590302934, (17, 20297): 175.88050817291676, (17, 20309): 189.04952675115766, (17, 20453): 200.7649276982779, (17, 20485): 170.98273186294966, (17, 20520): 169.00620302623673, (17, 20526): 168.34484609469408, (17, 20698): 82.95830126301185, (17, 20868): 69.03198252520033, (17, 21042): 149.96011407201487, (17, 21057): 154.67004102857817, (17, 21066): 152.43059803160472, (17, 21075): 151.44473971809185, (17, 21093): 150.41543936182936, (17, 21098): 153.90810200510427, (17, 21127): 150.40057414672668, (17, 21130): 151.33847508710133, (17, 21144): 151.1104551676155, (17, 21146): 150.0924553164339, (17, 21147): 151.00437636426017, (17, 21148): 151.85438706491854, (17, 21153): 149.5791157178385, (17, 21293): 157.89056690940672, (17, 21426): 156.01505542050793, (17, 21442): 160.9884894698986, (17, 21451): 161.47105661158847, (17, 21466): 158.50871415241258, (17, 21469): 159.26718389622138, (17, 21471): 158.1230826571335, (17, 21473): 158.75567625569, (17, 21475): 158.19598858954615, (17, 21482): 159.72749744835002, (17, 21484): 159.5794299859107, (17, 21488): 159.12969673618514, (17, 21494): 158.21823177036882, (17, 21498): 158.77667667303888, (17, 21500): 157.91505608469285, (17, 21514): 159.5436457257658, (17, 21537): 157.82121636095198, (17, 21662): 160.3084110659807, (17, 21691): 157.35618921868138, (17, 21757): 151.85611144383395, (17, 21777): 141.23426653597207, (17, 21778): 140.49376928427907, (17, 21779): 140.96446068991176, (17, 21790): 142.00825465328484, (17, 21802): 142.07836059513787, (17, 21824): 142.9048666525872, (17, 21874): 141.22829318074093, (17, 21879): 140.90358899266207, (17, 21983): 143.47617688708166, (17, 22002): 151.80956488807385, (17, 22132): 145.83547969985216, (17, 22261): 64.09064344663314, (17, 22298): 66.19805145942118, (17, 22339): 65.51180312157695, (17, 22508): 72.92103233088928, (17, 22841): 128.24987963990128, (17, 22842): 128.1212678743819, (17, 22874): 125.99059057365898, (17, 22941): 126.61197793138695, (17, 22956): 127.52290693852463, (17, 22960): 128.14239573400152, (17, 22968): 127.39339181137655, (17, 22970): 127.92474539753384, (17, 22974): 127.36931427503629, (17, 22980): 128.60629621560423, (17, 23025): 127.0242212325827, (17, 23028): 126.45416500744805, (17, 23081): 126.90686122307552, (17, 23104): 122.55698644961524, (17, 23147): 115.17604252661562, (17, 23298): 172.65049491017234, (17, 23376): 170.53432741912667, (17, 23381): 169.46407970930517, (17, 23529): 174.15438663091425, (17, 23556): 172.90680844635932, (17, 23718): 171.20620469723227, (17, 24001): 185.1494441438909, (17, 24094): 189.3839332471063, (17, 24129): 191.48339654858273, (17, 24174): 187.27243589500483, (17, 24235): 192.03469877389293, (17, 24259): 193.9368379256135, (17, 24260): 193.80181814064107, (17, 24261): 193.3372885453565, (17, 24305): 196.28957091582058, (17, 24306): 196.7151793285318, (17, 24307): 196.09219308839874, (17, 24308): 190.1849679373566, (17, 24498): 201.29972397744973, (17, 24499): 201.35239792505655, (17, 24500): 200.9567399503523, (17, 24668): 197.97787468430113, (17, 24711): 204.0962526504528, (17, 24756): 205.67269367519205, (17, 24788): 206.20151779432607, (17, 24809): 204.04647313487968, (17, 24813): 204.70141680047135, (17, 24821): 204.47819897827407, (17, 24825): 204.6779062502694, (17, 24832): 203.87307079656367, (17, 24833): 204.22121330573427, (17, 24835): 204.57855809823238, (17, 24837): 205.1079326682506, (17, 24840): 203.83203273287438, (17, 24841): 204.34339223640143, (17, 24844): 203.86536843669694, (17, 24845): 204.1144525483058, (17, 24846): 204.18018154574037, (17, 24849): 204.37827750510036, (17, 24850): 204.82886352722292, (17, 24863): 199.86093863176356, (17, 24866): 200.47642849612924, (17, 24885): 201.27252770626052, (17, 24886): 201.3648358277018, (17, 24889): 202.5901551363738, (17, 24903): 203.05791783953035, (17, 24909): 200.69619574603578, (17, 24999): 227.26769495488986, (17, 25019): 226.4098350756974, (17, 25028): 226.92977165113183, (17, 25137): 178.36307741516825, (17, 25145): 179.1691365205152, (17, 25208): 189.07071472096703, (17, 25233): 188.00056336964485, (17, 25371): 178.03392687134732, (17, 25377): 175.61392718608508, (17, 25828): 133.76310260517485, (17, 25851): 126.98686000426356, (17, 25874): 133.14251792716124, (17, 25898): 136.3015787511144, (17, 25946): 133.0886229921387, (17, 26047): 147.2073671191145, (17, 26066): 160.36029956828048, (17, 26197): 151.4540478729686, (17, 26212): 115.8497287587562, (17, 26253): 114.15837773963545, (17, 26254): 114.70202293382204, (17, 26257): 115.60945389079765, (17, 26258): 114.58913814273681, (17, 26260): 115.08967485519504, (17, 26266): 113.72132736367149, (17, 26267): 114.42916445731232, (17, 26271): 114.5380569839751, (17, 26304): 120.38499334535797, (17, 26305): 120.1263117662178, (17, 26363): 132.3347351666533, (17, 26441): 84.33154085945286, (17, 26442): 84.05424736068092, (17, 26450): 84.46308635378226, (17, 26459): 85.92308120097363, (17, 26462): 86.50024977063221, (17, 26467): 85.64173298718454, (17, 26471): 85.13727963306422, (17, 26472): 84.94836236050881, (17, 26473): 84.75129882625649, (17, 26476): 82.7650890059474, (17, 26485): 85.05059990367964, (17, 26493): 84.30262730037235, (17, 26524): 87.00313550821373, (17, 26525): 86.64619757359127, (17, 26556): 85.32265515854927, (17, 26560): 86.55633294861535, (17, 26561): 87.02054625056014, (17, 26564): 85.07416000635374, (17, 26569): 86.67054760931414, (17, 26570): 86.29004921808713, (17, 26573): 85.60039913306109, (17, 26581): 85.03862822010808, (17, 26583): 85.46004289931936, (17, 26593): 84.31624445065374, (17, 26837): 85.0010823873252, (17, 26844): 85.09377630092199, (17, 26863): 83.49855902747359, (17, 26893): 83.15933505632619, (17, 26902): 83.24536919743602, (17, 26905): 84.4270372923887, (17, 26912): 84.09346256168531, (17, 26921): 83.4156644159261, (17, 26922): 81.33127228255397, (17, 27212): 113.78148411224673, (17, 27218): 114.86927175620512, (17, 27239): 113.72252392789147, (17, 27257): 113.19168050859443, (17, 27274): 113.52361242439834, (17, 27279): 113.02892009107491, (17, 27282): 112.93883971343604, (17, 27283): 113.88445153774676, (17, 27285): 113.28633873616327, (17, 27286): 112.37928049144338, (17, 27290): 112.79033561334575, (17, 27295): 113.43935967106768, (17, 27300): 113.72567688666967, (17, 27344): 111.37712518726285, (17, 27366): 111.0061989840644, (17, 27383): 112.30863284947488, (17, 27398): 113.58244616391369, (17, 27406): 113.82109238731334, (17, 27407): 114.22799018503058, (17, 27426): 117.2621749186337, (17, 27432): 115.9095636300876, (17, 27460): 117.16894241085063, (17, 27523): 103.65319207168262, (17, 27545): 114.55580691442306, (17, 27602): 117.06039563834804, (17, 27606): 117.76080056457116, (17, 27646): 103.24107681563875, (17, 27667): 103.69640232475501, (17, 27672): 104.08867440366316, (17, 27674): 103.77341140484249, (17, 27688): 105.28298922948748, (17, 27692): 103.76566856450594, (17, 27693): 103.60786602915513, (17, 27705): 103.18879289584666, (17, 27712): 102.91524114691876, (17, 27786): 131.42946508327614, (17, 27790): 135.44666504307543, (17, 27791): 136.07106192629897, (17, 27795): 130.64714051088137, (17, 27801): 133.2199140362022, (17, 27813): 131.08922551673163, (17, 27816): 131.79684932244012, (17, 27823): 133.36033609781327, (17, 27830): 132.60208998304188, (17, 27884): 98.59674435233059, (17, 27885): 102.44726417534896, (17, 27896): 100.30739076919393, (17, 27919): 100.55758169776404, (17, 27922): 100.44317586186108, (17, 27930): 99.6770363355707, (17, 27934): 99.46503707382094, (17, 27935): 99.16410836341237, (17, 27948): 97.8336688494653, (17, 27951): 104.33305043732214, (17, 28061): 46.663334544380334, (17, 28290): 72.70001845221218, (17, 28292): 71.75236018539155, (17, 28293): 72.3867532239719, (17, 28295): 71.11221857100298, (17, 28296): 72.12840560306478, (17, 28297): 73.10196018944805, (17, 28302): 71.96665020055016, (17, 28310): 48.160229570596265, (17, 28313): 49.498397042823264, (17, 28372): 48.34674951292531, (17, 28398): 48.49843605023153, (17, 28399): 48.29876090617736, (17, 28400): 48.77310911290106, (17, 28401): 47.38349856996413, (17, 28445): 49.54145195740028, (17, 28475): 45.711600776905605, (17, 28885): 192.12068271487317, (17, 28886): 191.72015327403128, (17, 28915): 192.05876525387606, (17, 28916): 191.72300381526452, (17, 28917): 191.5057937106937, (17, 28921): 192.86459298177198, (17, 28931): 192.75451656449837, (17, 28945): 190.76951488903458, (17, 28982): 191.2519940262245, (17, 29219): 193.5439898098903, (17, 29228): 191.75450529534066, (17, 29246): 203.39628485779212, (17, 29248): 203.25279730115705, (17, 29282): 200.83456313865585, (17, 29290): 204.5626039195696, (17, 29291): 204.08318376478474, (17, 29292): 204.53430432376123, (17, 29293): 203.5904492412138, (17, 29294): 204.34795139626647, (17, 29298): 203.66592418088314, (17, 29299): 203.58939394249725, (17, 29304): 202.6984136061681, (17, 29317): 200.42862994530006, (17, 29323): 200.2520112462858, (17, 29330): 201.3460505440487, (17, 29331): 201.88636812728473, (17, 29344): 193.7738118634992, (17, 29445): 173.35390000319447, (17, 29724): 130.9084354729541, (17, 29738): 131.21169965197493, (17, 29745): 130.5494577410949, (17, 29748): 131.86440486370557, (17, 29750): 132.84297121796104, (17, 29759): 131.31064002516266, (17, 29772): 132.44166019767155, (17, 29781): 132.22748672836676, (17, 29784): 131.5429626683353, (17, 29790): 132.6762769766389, (17, 29811): 132.54823415029924, (17, 29817): 137.72849881069607, (17, 29818): 137.54689625751845, (17, 29929): 129.74518981276395, (17, 30039): 130.82562960885525, (17, 30066): 126.60608118021, (17, 30116): 118.34580415771956, (17, 30238): 107.31487150958223, (17, 30248): 109.13052694358048, (17, 30260): 108.97631527799008, (17, 30545): 185.94984428685976, (17, 30733): 166.6082394150225, (17, 30756): 161.8135578251863, (17, 30921): 170.9907047259632, (17, 31079): 120.61521554505521, (17, 31149): 118.2353895909474, (17, 31154): 118.24152354422097, (17, 31160): 118.09333638363915, (17, 31163): 117.93833399358975, (17, 31189): 110.080919942224, (17, 31215): 110.48644342743329, (17, 31259): 109.28056776987651, (17, 31262): 108.43667248411144, (17, 31430): 121.38491390010999, (17, 31568): 98.79806925269945, (17, 31751): 116.22173741303614, (25, 109): 55.14248268080962, (25, 872): 193.8148330744511, (25, 873): 194.71078925633554, (25, 877): 194.37170398474925, (25, 879): 194.50436883278118, (25, 884): 193.59800934826993, (25, 889): 194.1609868127693, (25, 891): 193.30206669556406, (25, 892): 195.19965938512144, (25, 894): 195.08765813101226, (25, 896): 194.22956989537295, (25, 903): 194.40226409484248, (25, 909): 192.88686317117353, (25, 910): 193.24897869832333, (25, 912): 192.65578927752873, (25, 913): 192.00085945637, (25, 916): 191.72910670639413, (25, 926): 193.547545798371, (25, 927): 193.2477311530319, (25, 948): 192.97758488399288, (25, 961): 193.50716622795642, (25, 962): 193.61119013216594, (25, 963): 193.72740320135838, (25, 967): 194.7822756313805, (25, 974): 194.2957245065636, (25, 998): 195.13493820461068, (25, 1014): 214.75300078322374, (25, 1086): 191.77576337243272, (25, 1087): 191.69087919631448, (25, 1089): 190.85194017310573, (25, 1090): 191.22623054599194, (25, 1092): 192.51393105650692, (25, 1097): 191.52636166012738, (25, 1107): 193.17224085082518, (25, 1387): 61.38571651050981, (25, 1554): 48.03061230792115, (25, 1827): 234.8327211927666, (25, 1828): 234.92796302018186, (25, 1829): 235.06658700002325, (25, 1830): 234.92640638502417, (25, 1831): 235.00676557024997, (25, 1832): 234.90943266735798, (25, 1833): 234.91985880422422, (25, 1836): 234.81541698399704, (25, 1841): 235.39385959664457, (25, 1843): 235.15177882849866, (25, 1844): 235.26003528553372, (25, 1845): 234.9722276544207, (25, 1847): 234.03789869934226, (25, 1848): 234.3593009022396, (25, 1849): 235.86633766881187, (25, 1850): 236.0236490945816, (25, 1851): 234.60654988881373, (25, 1852): 234.63133667287187, (25, 1854): 234.78430700002596, (25, 1856): 233.99359416657973, (25, 1857): 234.33792601647136, (25, 1858): 235.71902384133915, (25, 1861): 235.04713835796682, (25, 1866): 233.97410036139212, (25, 1867): 235.40963871129173, (25, 1868): 235.2144974194804, (25, 1870): 235.2349654607651, (25, 1871): 235.36489323429507, (25, 1875): 234.76718244846833, (25, 1880): 234.1939341722143, (25, 1882): 234.29059702621913, (25, 1883): 236.03476907412877, (25, 1889): 234.36024876048066, (25, 1893): 235.08265676242797, (25, 1894): 234.8551733470488, (25, 1899): 234.15922165547892, (25, 1900): 234.32639671846255, (25, 1902): 235.47694874717573, (25, 1905): 235.7706723813146, (25, 1907): 234.57686248973312, (25, 1910): 234.68379511203943, (25, 1917): 236.38486543542183, (25, 1920): 234.59799236805225, (25, 1935): 235.80903941678395, (25, 1937): 236.05906128144423, (25, 1946): 233.65245489724634, (25, 1949): 233.93143132933668, (25, 1950): 232.9524834833824, (25, 1951): 233.4253584178387, (25, 1952): 233.78296857312978, (25, 1953): 233.93399205266132, (25, 1954): 233.71301233101465, (25, 1958): 233.85302112540026, (25, 1960): 234.32841030947492, (25, 1968): 234.5160333407456, (25, 1969): 235.86459404197262, (25, 1974): 235.51208123597252, (25, 1975): 235.50919043775477, (25, 1979): 234.83338928749143, (25, 1980): 234.78333746810412, (25, 1981): 234.9784581374706, (25, 1985): 235.13994010245568, (25, 1994): 232.579112548582, (25, 2011): 234.28008522847236, (25, 2019): 236.64236847149547, (25, 2020): 236.32991246953424, (25, 2029): 235.14886515212362, (25, 2030): 236.1132765734623, (25, 2032): 234.95853861798773, (25, 2033): 235.58319895641014, (25, 2034): 235.57502383358246, (25, 2036): 234.40536336848308, (25, 2037): 234.7041025818588, (25, 2038): 234.7928352945691, (25, 2042): 238.38663920732384, (25, 2050): 235.41762082805232, (25, 2051): 235.3685224567509, (25, 2053): 235.46268090849597, (25, 2054): 235.7807198438249, (25, 2066): 235.13400020180129, (25, 2067): 235.13467064393183, (25, 2071): 231.9785289346856, (25, 2072): 232.57209250643734, (25, 2073): 230.9320474438225, (25, 2074): 230.85282896736047, (25, 2080): 229.85106805932472, (25, 2082): 232.89276017709648, (25, 2083): 233.19953414526816, (25, 2089): 232.54418877249617, (25, 2090): 232.82993325429618, (25, 2092): 232.43656933210053, (25, 2098): 230.23240818320673, (25, 2099): 230.58081035664523, (25, 2101): 230.17237807972495, (25, 2102): 231.79323157580183, (25, 2103): 231.28471265024174, (25, 2104): 231.00794969548366, (25, 2106): 233.40870233380178, (25, 2112): 230.39051223826561, (25, 2113): 232.02567586447117, (25, 2114): 232.4214372872482, (25, 2117): 233.65470065459644, (25, 2123): 231.21415720639507, (25, 2124): 231.5484208749265, (25, 2134): 230.59885887856066, (25, 2138): 231.58114687375587, (25, 2141): 230.71373666626093, (25, 2148): 231.2189268407126, (25, 2150): 229.90076893185554, (25, 2151): 230.25351173355847, (25, 2152): 229.71681807253412, (25, 2153): 231.32984864627406, (25, 2154): 229.94375589391012, (25, 2155): 229.78770240347015, (25, 2156): 229.52758141104766, (25, 2157): 229.89276797918092, (25, 2160): 232.05521582325156, (25, 2161): 229.66050807879463, (25, 2162): 231.39620430173954, (25, 2163): 230.9258967003017, (25, 2164): 230.89586486053383, (25, 2168): 230.04357774115635, (25, 2172): 230.364595935886, (25, 2174): 230.21483244383126, (25, 2178): 230.64181260966186, (25, 2179): 230.42647899641094, (25, 2183): 231.55977521158755, (25, 2185): 231.58168093873618, (25, 2186): 231.31440983311288, (25, 2190): 232.1189637124613, (25, 2192): 231.63794734133796, (25, 2193): 231.65302350512, (25, 2194): 231.1617889475843, (25, 2195): 231.09254176027406, (25, 2197): 231.74433239591272, (25, 2205): 231.0599753567789, (25, 2207): 230.16885130566646, (25, 2208): 230.6677371636377, (25, 2212): 231.79296431018375, (25, 2214): 221.91645745008043, (25, 2225): 223.10378532839349, (25, 2231): 220.74411694224966, (25, 2278): 228.01936939050353, (25, 2284): 229.0380375661261, (25, 2285): 228.89970644790074, (25, 2291): 226.91267913222694, (25, 2292): 227.10651653871804, (25, 2307): 228.38114517612843, (25, 2313): 226.68369391941232, (25, 2317): 226.3505581328086, (25, 2319): 227.456803171875, (25, 2321): 227.92515495118207, (25, 2323): 227.85746986931798, (25, 2326): 229.6152111660355, (25, 2327): 229.17729146126834, (25, 2329): 228.8789657480326, (25, 2330): 228.54044521516548, (25, 2332): 229.2646427314958, (25, 2344): 228.13985172212142, (25, 2346): 228.12317976234385, (25, 2361): 227.9270774785174, (25, 2368): 233.04782605738075, (25, 2374): 233.53256871054927, (25, 2375): 233.69200950981647, (25, 2377): 232.00670432783997, (25, 2378): 233.99717583722617, (25, 2379): 234.04328489173596, (25, 2380): 234.20687045914906, (25, 2383): 232.45364106669732, (25, 2385): 232.71234629446394, (25, 2395): 232.738505619604, (25, 2397): 233.8448606411127, (25, 2398): 231.4702190694252, (25, 2399): 232.07425314294204, (25, 2400): 231.93840530073615, (25, 2402): 232.9091666047362, (25, 2403): 233.28567317209968, (25, 2404): 233.38124079388965, (25, 2405): 232.4751747617349, (25, 2407): 233.21127982500798, (25, 2408): 233.65454134846823, (25, 2409): 232.74948440585237, (25, 2411): 233.28883291326557, (25, 2412): 233.1877659215087, (25, 2413): 233.49751782242015, (25, 2414): 232.99606211870758, (25, 2422): 233.17628757657556, (25, 2424): 233.29277927271258, (25, 2426): 233.3731928436866, (25, 2433): 232.67359369565807, (25, 2436): 232.49067947223645, (25, 2437): 230.29115015677147, (25, 2440): 230.77488317886133, (25, 2445): 240.5410392669097, (25, 2447): 239.3397313633683, (25, 2454): 240.4662646589712, (25, 2455): 240.52551386233964, (25, 2460): 237.03194226618916, (25, 2461): 237.46384680708277, (25, 2471): 244.46476685440936, (25, 2492): 237.24970301043837, (25, 2511): 233.70289764002095, (25, 2523): 235.5168465934099, (25, 2525): 235.00015273274144, (25, 2535): 235.81374177875466, (25, 2537): 235.04192020761514, (25, 2538): 235.5715004574764, (25, 2539): 235.360794525713, (25, 2540): 236.16426674751622, (25, 2542): 236.7283722989715, (25, 2559): 247.69968474394503, (25, 2575): 246.72031058989947, (25, 2599): 230.04629306171182, (25, 2600): 233.77616929407222, (25, 2607): 231.61777416047764, (25, 2627): 235.9526001938534, (25, 2647): 238.02500289781517, (25, 2674): 236.9389995352897, (25, 2681): 236.66858514453276, (25, 2683): 237.6632857953387, (25, 2686): 236.5062464778737, (25, 2689): 249.88168751597263, (25, 2690): 249.95073653889625, (25, 2713): 252.68557311635084, (25, 2714): 252.9349197212705, (25, 2715): 253.26285671094394, (25, 2739): 252.96471812979178, (25, 2740): 250.83006775383413, (25, 2741): 250.9887734009954, (25, 2749): 252.53808485382652, (25, 2750): 252.63167810137017, (25, 2752): 252.86153341004928, (25, 2755): 253.12657858306716, (25, 2758): 253.05842665121762, (25, 2759): 253.0555041063549, (25, 2769): 252.66419791957784, (25, 2771): 251.37637206449463, (25, 2779): 251.54163184057114, (25, 2784): 247.87385983877698, (25, 2800): 248.60462063013296, (25, 2802): 250.2269318968611, (25, 2803): 250.09417057255456, (25, 2804): 249.87163171171613, (25, 2805): 250.52774859956446, (25, 2807): 250.4990475074214, (25, 2809): 250.39519384521085, (25, 2812): 248.26612579363166, (25, 2814): 250.34118737429827, (25, 2817): 250.49600681818987, (25, 2819): 250.5221589870769, (25, 2823): 248.54424157154062, (25, 2832): 250.94768360163243, (25, 2836): 249.46681857776122, (25, 2839): 250.48607844474589, (25, 2841): 250.52656999577513, (25, 2843): 250.40194655947758, (25, 2846): 249.79328969205068, (25, 2849): 251.19289924074644, (25, 2852): 250.85120782479166, (25, 2853): 251.35070886774724, (25, 2876): 251.54080017129573, (25, 2877): 252.73488857606114, (25, 2885): 253.18186412105192, (25, 2918): 250.64007336841246, (25, 2921): 251.16046566218571, (25, 2925): 248.69474398920025, (25, 2926): 247.85923586636923, (25, 2930): 249.78699099901766, (25, 2931): 248.93614187244472, (25, 2938): 250.66014323112978, (25, 2940): 252.08263975686748, (25, 2947): 250.32035409441002, (25, 2949): 249.74078717995758, (25, 2950): 249.98411023978412, (25, 2952): 249.73205738984453, (25, 2958): 249.67727575576703, (25, 2959): 249.90514628059935, (25, 2960): 250.47262078745524, (25, 2961): 250.20877633760037, (25, 2963): 249.47126008991762, (25, 2968): 249.6400607348543, (25, 2976): 249.3958634536624, (25, 2981): 244.69844074672872, (25, 2982): 244.5785815025281, (25, 2984): 244.33333946083252, (25, 3003): 243.91589567799883, (25, 3046): 240.4505286583948, (25, 3050): 243.106797932569, (25, 3051): 243.29757226115353, (25, 3053): 242.75422305924485, (25, 3069): 245.86099748441094, (25, 3071): 242.58233687912346, (25, 3080): 253.2233191308414, (25, 3199): 243.22621988481535, (25, 3200): 242.66033364029548, (25, 3205): 246.22675260770652, (25, 3209): 242.96623942501364, (25, 3215): 242.68390004505477, (25, 3217): 241.97243819677652, (25, 3249): 242.73571897080976, (25, 3263): 248.10289520940987, (25, 3289): 244.3985787537063, (25, 3301): 244.600971010163, (25, 3302): 244.33288792143708, (25, 3307): 244.01005668640155, (25, 3310): 244.90729063167294, (25, 3391): 246.28747085478744, (25, 3509): 128.98943084253807, (25, 3510): 128.4784327830633, (25, 3511): 128.80593033069863, (25, 3512): 128.4788747842995, (25, 3514): 128.576597260005, (25, 3519): 130.25591705147232, (25, 3536): 129.8685600575608, (25, 3545): 130.65806036805046, (25, 3548): 129.85903659427316, (25, 3572): 130.1740465444987, (25, 3581): 129.5997506238126, (25, 3583): 129.19716315739473, (25, 3601): 131.23889835398197, (25, 3656): 130.47113780544046, (25, 3669): 129.62410103159215, (25, 3670): 130.08926428510009, (25, 3695): 127.4041898267281, (25, 3696): 127.76348466210094, (25, 3782): 129.89582918352875, (25, 3792): 129.35011150509914, (25, 3989): 91.0193589719085, (25, 4008): 93.81900194160505, (25, 4031): 93.7845785388091, (25, 4045): 92.64992825981669, (25, 4144): 92.68330185568117, (25, 4145): 89.77839918080328, (25, 4164): 91.57739610400655, (25, 4168): 90.6580572713493, (25, 4173): 90.45817389131993, (25, 4181): 88.76070585656613, (25, 4228): 87.25761521143203, (25, 4248): 86.4319407031399, (25, 4254): 71.44468211850143, (25, 4260): 71.45531398223387, (25, 4262): 72.43665444417431, (25, 4273): 72.20310464662737, (25, 4319): 63.63908526618518, (25, 4326): 63.327014141210206, (25, 4328): 63.414298989851005, (25, 4334): 64.03676993400096, (25, 4335): 63.845798324725415, (25, 4372): 91.74050570332315, (25, 4413): 100.86628507763226, (25, 4434): 91.04220415858376, (25, 4447): 90.94740056379355, (25, 4452): 91.3297336684128, (25, 4463): 84.28401198276046, (25, 4465): 84.23142814379888, (25, 4619): 105.23481591256382, (25, 4645): 106.07047257295183, (25, 4657): 106.2852686541818, (25, 4666): 106.14068600081158, (25, 4676): 107.08771538523999, (25, 4678): 107.09590110874093, (25, 4689): 106.96239585167234, (25, 4704): 111.81542876110862, (25, 4726): 132.37163489999517, (25, 4727): 132.0308037356017, (25, 4730): 131.34373577075476, (25, 4731): 131.71228452263173, (25, 4734): 131.10859610261954, (25, 4735): 130.93201982278268, (25, 4736): 131.222321767366, (25, 4737): 130.8226826231081, (25, 4738): 131.0024042507668, (25, 4756): 131.42165866141895, (25, 4760): 128.99320557710243, (25, 4761): 128.89926554079992, (25, 4762): 128.7015617590845, (25, 4765): 129.24703577167088, (25, 4773): 132.89997410992035, (25, 4774): 132.82683680750844, (25, 4790): 132.63908609638963, (25, 4795): 132.28381744168695, (25, 4799): 133.09640943821984, (25, 4801): 134.12566675928585, (25, 4804): 132.11172187937217, (25, 4805): 131.82325288738826, (25, 4806): 133.03862340730745, (25, 4815): 132.91651016826452, (25, 4816): 133.6634179932114, (25, 4817): 134.09877792178494, (25, 4826): 133.50921257650884, (25, 4830): 133.14008133106907, (25, 4839): 129.99910639416288, (25, 4840): 130.4171103582054, (25, 4841): 129.79220745240337, (25, 4846): 129.5111037909525, (25, 4848): 129.664077979596, (25, 4850): 130.01272942250355, (25, 4871): 125.00782177569647, (25, 4883): 128.2751921137759, (25, 4900): 126.27291557622418, (25, 4901): 126.0319407907249, (25, 4917): 110.00010828699654, (25, 4931): 107.87236772563132, (25, 4944): 110.05440036793335, (25, 4956): 108.45078418554235, (25, 4958): 108.7638789275204, (25, 4959): 108.61940286628754, (25, 4961): 108.7285648374565, (25, 4966): 108.14949681574062, (25, 5207): 105.84643494670013, (25, 5272): 52.282615978178306, (25, 5283): 53.19341848086646, (25, 5287): 55.709137006013925, (25, 5289): 56.14622913341812, (25, 5293): 51.40532743403535, (25, 5295): 53.823419357260235, (25, 5296): 54.44164715774808, (25, 5298): 54.769910926128944, (25, 5303): 56.027463734627666, (25, 5305): 53.074957960869014, (25, 5306): 53.373823642895054, (25, 5307): 52.69148101431816, (25, 5308): 53.68369493541357, (25, 5313): 52.80767436067266, (25, 5314): 53.09803541557058, (25, 5317): 54.126684388744806, (25, 5319): 55.35924683933962, (25, 5324): 54.3809769281881, (25, 5326): 53.71358883297451, (25, 5348): 53.7668835594606, (25, 5351): 55.34722175802376, (25, 5399): 57.58131468464796, (25, 5413): 57.92910837023176, (25, 5422): 57.39024433356168, (25, 5445): 55.75339307719187, (25, 5448): 54.964693297257874, (25, 5456): 55.4893278159848, (25, 5467): 56.40620934886306, (25, 5624): 45.49601208063343, (25, 5671): 64.20032434545067, (25, 5672): 62.96682478908106, (25, 5797): 78.45428297597535, (25, 5871): 74.69824297490933, (25, 5976): 65.97329799201269, (25, 6118): 192.53924708645548, (25, 6248): 204.42379144027683, (25, 6345): 24.43479941896955, (25, 6352): 26.637835773860232, (25, 6354): 23.677108904321077, (25, 6359): 23.66527222759956, (25, 6376): 27.255286996250053, (25, 6378): 23.98021314371626, (25, 6381): 24.127981429855982, (25, 6383): 24.73558005669081, (25, 6396): 26.03139898711096, (25, 6399): 24.900230831377232, (25, 6408): 26.16713198085218, (25, 6409): 24.085554209959156, (25, 6419): 26.334906756001704, (25, 6422): 25.069682123027018, (25, 6423): 25.196852885519384, (25, 6424): 22.69382313869595, (25, 6439): 22.784845989363497, (25, 6464): 23.089615825023333, (25, 6465): 23.663770306122107, (25, 6469): 24.1314669948751, (25, 6470): 24.442098438415346, (25, 6472): 23.11495115851771, (25, 6480): 21.736160873444124, (25, 6486): 18.553051440097455, (25, 6497): 19.52948445546615, (25, 6503): 20.954552556720476, (25, 6508): 21.85099359904353, (25, 6509): 20.914672167494505, (25, 6521): 20.665841416810327, (25, 6544): 19.72703420645139, (25, 6552): 22.9084964335556, (25, 6553): 23.16431096180803, (25, 6554): 23.440956795826224, (25, 6578): 22.638793440674057, (25, 6582): 21.78983215092113, (25, 6601): 22.29357898810399, (25, 6609): 21.387542438127745, (25, 6610): 21.06271712740162, (25, 6611): 21.674661226616006, (25, 6614): 22.199611303768272, (25, 6615): 21.92239140507184, (25, 6616): 20.802017090789473, (25, 6617): 21.219051910734557, (25, 6618): 19.978548053210737, (25, 6619): 22.245762316094762, (25, 6620): 20.38666594750258, (25, 6621): 20.522229316929636, (25, 6622): 20.752254813033698, (25, 6623): 21.772434175860663, (25, 6624): 21.537784649958407, (25, 6625): 21.79750111765486, (25, 6626): 22.437175044096055, (25, 6627): 22.613419748819712, (25, 6628): 20.017920902194707, (25, 6629): 20.980745025030284, (25, 6630): 22.636329831551368, (25, 6632): 21.227220223301952, (25, 6634): 22.611889999686017, (25, 6635): 20.820153596870313, (25, 6636): 20.647606628919306, (25, 6637): 21.243970263211637, (25, 6638): 22.22260228845576, (25, 6639): 22.349776288505915, (25, 6640): 22.391746030050623, (25, 6641): 20.21210453639951, (25, 6642): 21.947928256563543, (25, 6643): 22.754752742379782, (25, 6645): 22.029360990641383, (25, 6646): 20.37997729538489, (25, 6647): 22.031665503329965, (25, 6653): 22.05929195025204, (25, 6655): 22.48205417190827, (25, 6658): 22.471019490413138, (25, 6662): 21.672628682816303, (25, 6819): 33.564401522726044, (25, 6996): 24.980435687453145, (25, 7059): 20.79584395748096, (25, 7187): 29.111658089432964, (25, 7304): 36.28311864130837, (25, 7528): 24.618914779345822, (25, 7720): 12.5, (25, 7793): 12.5, (25, 7807): 12.5, (25, 7808): 12.5, (25, 7831): 17.00679584426796, (25, 7850): 17.033536694731406, (25, 7852): 18.086096822918, (25, 8012): 12.5, (25, 8125): 13.287913797860123, (25, 8208): 12.5, (25, 8392): 12.5, (25, 8651): 53.09060495426174, (25, 9088): 39.708808072162874, (25, 9443): 61.2318599540312, (25, 9444): 60.69467305342859, (25, 9828): 81.27700443781954, (25, 9868): 80.19157519254689, (25, 10180): 14.653532530593834, (25, 10256): 22.012025161202462, (25, 10276): 16.26595732372402, (25, 10378): 12.5, (25, 10676): 24.82146550679405, (25, 10714): 27.768260459727585, (25, 10730): 19.638183199092474, (25, 10862): 92.65711783872815, (25, 10881): 93.12663391153295, (25, 10883): 93.32450939467687, (25, 10885): 92.49604025084628, (25, 10891): 93.64056957361666, (25, 10909): 93.00062713335593, (25, 10911): 92.45237190317705, (25, 10913): 92.54143919396866, (25, 10915): 92.21930435047511, (25, 10919): 92.01889068873258, (25, 11037): 97.05000905099915, (25, 11039): 93.62699534544544, (25, 11516): 123.14374051695401, (25, 11856): 64.29945881549557, (25, 11857): 63.96498945784757, (25, 11861): 64.14612200886714, (25, 11881): 63.62128440746658, (25, 11902): 61.751187683835546, (25, 11911): 61.380602015913624, (25, 11914): 61.65224907946086, (25, 11922): 63.053737373370474, (25, 11924): 63.48569431678861, (25, 11926): 62.94509895334466, (25, 11950): 63.98353273970745, (25, 11963): 65.74567698687042, (25, 11983): 64.537159809488, (25, 11985): 66.63189184464305, (25, 12009): 66.26545378058884, (25, 12010): 65.01961697230944, (25, 12018): 65.2241434361938, (25, 12020): 65.56421340458238, (25, 12021): 65.7698016684333, (25, 12024): 66.96266273002162, (25, 12025): 66.56230708861916, (25, 12027): 66.27889967428604, (25, 12031): 64.8108948618792, (25, 12032): 65.22818632402367, (25, 12035): 66.18583661565812, (25, 12041): 66.81271545698547, (25, 12045): 50.18454289842782, (25, 12145): 57.84214889519053, (25, 12275): 92.59797199607397, (25, 12294): 89.98814432984467, (25, 12358): 99.83019871825998, (25, 12463): 103.94215214771098, (25, 12465): 103.86109854145988, (25, 12482): 105.06005617872158, (25, 12503): 104.93486133557718, (25, 12506): 105.36028618913224, (25, 12549): 103.98512033109567, (25, 12559): 103.74786737654681, (25, 12569): 104.25773453433608, (25, 12572): 104.5689145647208, (25, 12574): 103.86838332544461, (25, 12576): 104.30407147847434, (25, 12591): 103.98229396731878, (25, 12608): 106.4202751683455, (25, 12696): 102.08653164638403, (25, 12710): 104.24671095635166, (25, 12728): 103.36068817826877, (25, 12766): 37.78522108530186, (25, 12771): 32.502835828559924, (25, 12790): 32.27849957850402, (25, 12795): 32.155430455517816, (25, 12797): 27.247985318461055, (25, 12798): 27.539642722850473, (25, 12811): 30.246352941199298, (25, 12830): 29.88141284455733, (25, 12848): 29.237306883782303, (25, 12850): 28.822454217255764, (25, 12852): 29.412480225232112, (25, 12854): 29.009448780911978, (25, 12859): 29.3725793102511, (25, 12861): 27.713980277122715, (25, 12865): 31.24389247695965, (25, 12866): 30.704885833037274, (25, 12867): 31.83638304580018, (25, 12874): 31.331832201771302, (25, 12875): 31.51413817279936, (25, 12881): 30.5952421264425, (25, 12883): 31.065027541845524, (25, 12885): 31.86531488694319, (25, 12888): 30.612369509501722, (25, 12889): 30.283364850481213, (25, 12892): 31.545612952404074, (25, 12893): 30.856579735478608, (25, 12896): 30.874331022569965, (25, 12906): 32.354823421518915, (25, 13018): 35.74836970801808, (25, 13071): 37.35115043351489, (25, 13131): 28.82383415528468, (25, 13146): 29.476007015365305, (25, 13159): 35.42118511573402, (25, 13193): 28.01470185277823, (25, 13198): 22.734947688877597, (25, 13292): 25.052955994591933, (25, 13296): 23.6462003308631, (25, 13406): 26.93320027029058, (25, 13407): 27.312982786050778, (25, 13417): 30.440947996919828, (25, 13418): 31.00889426249796, (25, 13438): 28.906417816358616, (25, 13442): 27.967419522222873, (25, 13443): 28.000461285789715, (25, 13764): 65.80173319161179, (25, 13766): 65.31031204371865, (25, 13771): 66.6790254229475, (25, 13783): 64.75198777875107, (25, 13784): 64.39171220131976, (25, 13792): 68.96104058463168, (25, 13824): 65.27178901689082, (25, 14017): 57.269324920788925, (25, 14870): 79.79063971126405, (25, 14997): 32.41461567498967, (25, 15000): 32.52317300542959, (25, 15003): 32.29601737336904, (25, 15006): 30.619963209645263, (25, 15007): 30.2104044238281, (25, 15056): 30.775003033930794, (25, 15063): 31.25504696712808, (25, 15069): 31.616337063498747, (25, 15076): 30.254740923200853, (25, 15086): 31.400702845278072, (25, 15087): 32.0600566181768, (25, 15111): 33.208518799158114, (25, 15116): 32.55868872334552, (25, 15722): 44.052137040992896, (25, 15998): 55.66064906590843, (25, 16073): 156.65748429744585, (25, 16939): 206.40539241273194, (25, 16940): 205.7402083172108, (25, 16951): 206.51056060648344, (25, 16963): 206.57113086653874, (25, 16965): 207.37509048071695, (25, 16969): 207.18711485163243, (25, 16970): 206.8595816289745, (25, 16971): 206.13467599871282, (25, 16973): 206.0910910003256, (25, 16974): 207.70297454236882, (25, 16976): 206.91277646109842, (25, 16978): 206.38145319355186, (25, 16980): 207.17686146634028, (25, 16982): 207.7026835668441, (25, 17045): 230.90855030559112, (25, 17048): 231.8469756602407, (25, 17304): 82.35235570155321, (25, 17305): 81.95706695076075, (25, 17330): 82.37599591776585, (25, 17334): 81.43507099786845, (25, 17343): 83.06994357064819, (25, 17345): 81.47288566767132, (25, 17347): 82.3650806466178, (25, 17351): 80.2044641513757, (25, 17372): 81.3593319081171, (25, 17373): 83.00499260384603, (25, 17377): 83.12693280613203, (25, 17382): 82.07025372395857, (25, 17383): 82.24188713551291, (25, 17389): 81.62427112190026, (25, 17400): 82.68777059878666, (25, 17401): 82.65559342068129, (25, 17402): 82.75717465781977, (25, 17403): 82.868426640307, (25, 17440): 81.62938052317469, (25, 17455): 82.93890839877385, (25, 17491): 83.10698461008054, (25, 17507): 80.69158138997685, (25, 17509): 81.26804290115486, (25, 17590): 79.89249203597407, (25, 17615): 76.4448219714806, (25, 17642): 77.02182721943092, (25, 17643): 76.96816885211672, (25, 17668): 76.42632433396894, (25, 17721): 75.14522452045398, (25, 17754): 80.6601966602192, (25, 17769): 80.85957815483832, (25, 17776): 78.58139776036546, (25, 17804): 81.80589326702759, (25, 17809): 82.39205621779723, (25, 17824): 82.00515689187883, (25, 17837): 80.37393119086083, (25, 17838): 80.46447941085701, (25, 17862): 80.0423854865185, (25, 17866): 81.27694723034334, (25, 17872): 79.60322673549452, (25, 17873): 78.66651070171895, (25, 17881): 80.108355654423, (25, 17947): 152.15740920918412, (25, 17951): 150.89894316754865, (25, 17953): 150.6578964101041, (25, 17954): 150.74571887774349, (25, 17959): 151.89994927894935, (25, 17963): 151.4591718717273, (25, 18000): 145.06436256790735, (25, 18001): 145.3119657059558, (25, 18111): 163.64609003524816, (25, 18148): 131.3667758052686, (25, 18166): 143.971425956341, (25, 18189): 155.49307862564964, (25, 18239): 83.27594500437671, (25, 18240): 83.2735396964528, (25, 18245): 83.3332567018039, (25, 18247): 83.20960437591962, (25, 18251): 83.33676107002587, (25, 18256): 83.4803320398226, (25, 18258): 83.33570791009535, (25, 18259): 83.36505692068502, (25, 18260): 83.42630063367247, (25, 18262): 83.5389626865539, (25, 18263): 83.52191694054635, (25, 18264): 83.58242863784376, (25, 18266): 83.58760058447558, (25, 18267): 83.64634525523664, (25, 18268): 83.67738541857274, (25, 18269): 83.7953563488346, (25, 18275): 83.73969603761057, (25, 18285): 83.55981343205875, (25, 18308): 82.34159482937946, (25, 18313): 81.94181666944321, (25, 18314): 82.13408295223823, (25, 18315): 83.77353341528638, (25, 18316): 83.77143214186204, (25, 18317): 83.82703478998747, (25, 18320): 83.86835994672526, (25, 18321): 83.90229933797892, (25, 18322): 83.98839062848387, (25, 18324): 84.04758280272988, (25, 18325): 84.30456159765863, (25, 18326): 84.20846834648643, (25, 18327): 83.88468743932026, (25, 18329): 84.41162757369153, (25, 18330): 84.30725401341782, (25, 18331): 84.1311787988364, (25, 18332): 83.95402213272521, (25, 18333): 84.27328144945216, (25, 18336): 84.117555452654, (25, 18337): 84.2001367394888, (25, 18403): 84.11528858091678, (25, 18432): 80.9528151269308, (25, 18451): 83.07910593367701, (25, 18466): 85.20502720807838, (25, 18481): 83.82157294190819, (25, 18483): 83.82645131585387, (25, 18484): 83.68136538611, (25, 18485): 83.24078910353548, (25, 18486): 83.60354024480252, (25, 18487): 83.27067711891581, (25, 18489): 83.5791239948968, (25, 18490): 83.89442781103213, (25, 18491): 84.04885183935583, (25, 18492): 82.94429286745641, (25, 18493): 83.54369290975396, (25, 18494): 83.52012670788014, (25, 18495): 83.77870693591609, (25, 18496): 83.62045664462916, (25, 18497): 83.19045570907285, (25, 18498): 83.2826263662016, (25, 18499): 83.52486938752669, (25, 18501): 83.34183374276158, (25, 18502): 83.18651742354191, (25, 18503): 83.07248248892391, (25, 18504): 83.69000115076493, (25, 18506): 83.35321760317211, (25, 18507): 83.20318569359364, (25, 18508): 83.4867677439887, (25, 18509): 83.48571231735598, (25, 18510): 83.07057075239486, (25, 18511): 83.58208926048798, (25, 18512): 83.4070827200106, (25, 18515): 83.69815228186857, (25, 18516): 83.69613202645789, (25, 18517): 83.49453372223894, (25, 18518): 83.8275453806241, (25, 18519): 83.72624761423624, (25, 18520): 83.44637806683355, (25, 18522): 84.39487339444895, (25, 18523): 84.42258567560731, (25, 18532): 84.62923944963732, (25, 18535): 84.19398477572162, (25, 18537): 83.95169222164385, (25, 18539): 83.99926032397725, (25, 18540): 84.0242458036998, (25, 18541): 84.14094665891157, (25, 18542): 84.21561790805335, (25, 18543): 83.842456648084, (25, 18546): 84.01009978160685, (25, 18555): 84.38985216036723, (25, 18556): 84.45532611304715, (25, 18565): 84.59329537454562, (25, 18567): 84.6934049253981, (25, 18568): 84.49087846502233, (25, 18577): 85.97930227312085, (25, 18583): 85.74447602504142, (25, 18605): 86.0766450260678, (25, 18608): 84.8012101184802, (25, 18616): 87.46352867627498, (25, 18618): 88.63545582389615, (25, 18625): 88.27407492784226, (25, 18645): 87.25257623684664, (25, 18646): 87.50732022739203, (25, 18653): 86.47703974155014, (25, 18654): 87.42648331653218, (25, 18655): 86.7936865112264, (25, 18666): 90.7068199845142, (25, 18837): 88.24714887998242, (25, 18974): 83.33666920750132, (25, 18999): 84.49936131843214, (25, 19000): 84.85459249042957, (25, 19174): 70.10930595074473, (25, 19342): 77.77826156436988, (25, 19455): 71.09629742250232, (25, 19555): 55.7011542156286, (25, 19564): 58.25363286022793, (25, 19573): 57.20930314088045, (25, 19586): 56.63778354147332, (25, 19605): 56.64144861782433, (25, 19611): 57.28265104823081, (25, 19614): 56.56235933864829, (25, 19641): 65.38536508421274, (25, 19702): 65.69190103334343, (25, 19713): 64.95002113225843, (25, 19731): 50.85580310873044, (25, 19819): 69.1359344100339, (25, 19893): 52.68400078331894, (25, 19899): 57.820885307512995, (25, 19929): 53.67318870949434, (25, 19951): 62.60059735789884, (25, 19962): 55.08815444388798, (25, 19970): 55.69057295704656, (25, 19971): 56.032225982041005, (25, 19972): 55.50673461367068, (25, 19975): 54.93842252834311, (25, 19978): 63.16643210551442, (25, 19987): 63.13645037637852, (25, 19989): 60.69785296654047, (25, 20039): 63.49748787863798, (25, 20043): 64.2716477557928, (25, 20047): 63.2820937376858, (25, 20052): 60.78026653210237, (25, 20054): 61.106758871342954, (25, 20085): 71.7969785104022, (25, 20104): 72.50999043918978, (25, 20132): 68.3603546247958, (25, 20203): 55.438630731634206, (25, 20280): 55.62198724578572, (25, 20285): 55.87970184492058, (25, 20290): 55.80418593303857, (25, 20297): 54.91614466701445, (25, 20309): 65.87746724213463, (25, 20453): 76.3853654946177, (25, 20485): 49.45533223295015, (25, 20520): 47.1577595000492, (25, 20526): 47.680992014978905, (25, 20698): 94.16775071145106, (25, 20868): 114.3616644848495, (25, 21042): 20.572593205609337, (25, 21057): 25.44088292077988, (25, 21066): 22.935206792007524, (25, 21075): 22.20434457992, (25, 21093): 20.79487907674041, (25, 21098): 24.13545418563036, (25, 21127): 20.88552832708983, (25, 21130): 21.73963275565491, (25, 21144): 21.73810452092559, (25, 21146): 20.569182720372506, (25, 21147): 21.711884127972457, (25, 21148): 22.4913256594431, (25, 21153): 21.694125389049216, (25, 21293): 28.41458192341738, (25, 21426): 30.726980011303432, (25, 21442): 36.68280930444659, (25, 21451): 37.23032035533746, (25, 21466): 33.39125728200399, (25, 21469): 34.00447305567536, (25, 21471): 33.09479382330598, (25, 21473): 33.531963415813294, (25, 21475): 33.065675131710485, (25, 21482): 34.61149742915013, (25, 21484): 34.36827350481312, (25, 21488): 34.06846848210019, (25, 21494): 32.75562790273613, (25, 21498): 33.293121025244766, (25, 21500): 32.207279411427805, (25, 21514): 32.626719127161536, (25, 21537): 31.431449923670367, (25, 21662): 32.689729765716656, (25, 21691): 29.853799798170385, (25, 21757): 27.237996080732827, (25, 21777): 12.5, (25, 21778): 12.5, (25, 21779): 12.5, (25, 21790): 12.5, (25, 21802): 12.5, (25, 21824): 13.359445649651756, (25, 21874): 12.5, (25, 21879): 12.5, (25, 21983): 13.766834199593506, (25, 22002): 21.971971406181485, (25, 22132): 20.31033176122788, (25, 22261): 90.86902810950517, (25, 22298): 89.72779031030431, (25, 22339): 99.40732697573904, (25, 22508): 76.23185998965026, (25, 22841): 245.40880511649806, (25, 22842): 245.4048455550567, (25, 22874): 243.5678695255046, (25, 22941): 243.779100755072, (25, 22956): 244.87878139201652, (25, 22960): 245.22332702698364, (25, 22968): 246.20878292333342, (25, 22970): 246.52767602661694, (25, 22974): 247.00554317553903, (25, 22980): 248.33371086591836, (25, 23025): 248.1005726626043, (25, 23028): 247.7832813963797, (25, 23081): 249.89615638256333, (25, 23104): 247.33802885099897, (25, 23147): 235.87076786753806, (25, 23298): 44.30145931742794, (25, 23376): 42.137238065938, (25, 23381): 40.383422622133686, (25, 23529): 45.29231228756419, (25, 23556): 44.09363196010168, (25, 23718): 43.502279490500456, (25, 24001): 57.21633542619751, (25, 24094): 60.492788199142375, (25, 24129): 62.633727826057104, (25, 24174): 58.02716312703383, (25, 24235): 62.69809178264863, (25, 24259): 64.81202621041157, (25, 24260): 64.64570914000826, (25, 24261): 64.20021826310166, (25, 24305): 67.28906765488288, (25, 24306): 67.68150379651864, (25, 24307): 67.07108207761136, (25, 24308): 63.219621444880936, (25, 24498): 73.09734141731334, (25, 24499): 73.1317688033808, (25, 24500): 72.75011282321616, (25, 24668): 70.89816531176889, (25, 24711): 75.52561709939727, (25, 24756): 76.82918027803342, (25, 24788): 77.48564036522977, (25, 24809): 75.0244559093934, (25, 24813): 75.79362627809718, (25, 24821): 75.54248365529041, (25, 24825): 75.7185112804366, (25, 24832): 74.86561816498852, (25, 24833): 75.23335598963513, (25, 24835): 75.59715918913753, (25, 24837): 76.18944912608848, (25, 24840): 74.8059650627555, (25, 24841): 75.38029029195658, (25, 24844): 74.81927357436545, (25, 24845): 75.1696529602471, (25, 24846): 75.11694362643921, (25, 24849): 75.3155394333671, (25, 24850): 75.90021107922843, (25, 24863): 70.81204615705369, (25, 24866): 71.47098224585889, (25, 24885): 72.2375420450995, (25, 24886): 72.28736732416866, (25, 24889): 73.7649446709904, (25, 24903): 74.34801132807381, (25, 24909): 71.96994265641872, (25, 24999): 101.4287908994395, (25, 25019): 100.82697889783968, (25, 25028): 100.98901894487956, (25, 25137): 62.49084177130501, (25, 25145): 63.03677424720201, (25, 25208): 74.57207586468152, (25, 25233): 73.96375780774353, (25, 25371): 59.20949339110381, (25, 25377): 56.53383879065022, (25, 25828): 33.697115023592296, (25, 25851): 30.200330763193644, (25, 25874): 31.189526340723, (25, 25898): 35.02372485140853, (25, 25946): 33.430751469944575, (25, 26047): 43.10987035775812, (25, 26066): 38.27891642605294, (25, 26197): 37.80618034640183, (25, 26212): 48.97936612941393, (25, 26253): 50.870509045353714, (25, 26254): 49.89720915749074, (25, 26257): 50.03489892518806, (25, 26258): 50.71700744977837, (25, 26260): 50.30451013845814, (25, 26266): 49.22656791335268, (25, 26267): 49.006313973804296, (25, 26271): 49.21231854669544, (25, 26304): 41.970924612264895, (25, 26305): 41.4103144053372, (25, 26363): 37.910158953756536, (25, 26441): 98.77798979143752, (25, 26442): 98.4865478424349, (25, 26450): 97.33955322284615, (25, 26459): 97.48164074218982, (25, 26462): 97.74700825505445, (25, 26467): 101.1444602558616, (25, 26471): 100.07400770232458, (25, 26472): 99.93902779794486, (25, 26473): 99.86721336784017, (25, 26476): 98.99531296804659, (25, 26485): 97.94216342606592, (25, 26493): 97.86001878696203, (25, 26524): 98.36361437730103, (25, 26525): 98.16444676803387, (25, 26556): 99.62514823063066, (25, 26560): 99.7089927808645, (25, 26561): 99.02212437426805, (25, 26564): 99.25877244937506, (25, 26569): 98.77730242688038, (25, 26570): 98.40940663201532, (25, 26573): 98.49246445381596, (25, 26581): 98.37616815510964, (25, 26583): 98.17770218274802, (25, 26593): 98.27316280751643, (25, 26837): 101.28483521826672, (25, 26844): 102.10352675476264, (25, 26863): 100.11073612439463, (25, 26893): 102.3826253651426, (25, 26902): 103.4868701384799, (25, 26905): 102.55351623314804, (25, 26912): 103.35615471344856, (25, 26921): 101.21147860940863, (25, 26922): 98.71506557499377, (25, 27212): 112.28571061969723, (25, 27218): 111.62425845984174, (25, 27239): 113.73887840059196, (25, 27257): 112.85156082013792, (25, 27274): 113.99005199064776, (25, 27279): 113.71151009759075, (25, 27282): 112.82605306891774, (25, 27283): 113.38929086219244, (25, 27285): 114.32555521372274, (25, 27286): 113.32380519052444, (25, 27290): 112.05132795229495, (25, 27295): 111.6714366517905, (25, 27300): 114.18600524239929, (25, 27344): 111.32183519056234, (25, 27366): 112.22032493832673, (25, 27383): 114.17564508218456, (25, 27398): 115.52073252987547, (25, 27406): 114.71938393594218, (25, 27407): 115.06856851507378, (25, 27426): 114.66844237915478, (25, 27432): 110.61713469512713, (25, 27460): 113.2605944661447, (25, 27523): 110.92074095505866, (25, 27545): 128.4930801940191, (25, 27602): 148.11001129542942, (25, 27606): 148.5816261401083, (25, 27646): 125.8311216832693, (25, 27667): 129.83943490153865, (25, 27672): 130.11149416162002, (25, 27674): 129.38958878719626, (25, 27688): 130.2079758696328, (25, 27692): 130.73464581032312, (25, 27693): 130.1213541641367, (25, 27705): 130.02014097533902, (25, 27712): 130.26333473361697, (25, 27786): 151.59413854881424, (25, 27790): 150.28996668718514, (25, 27791): 150.2414421559777, (25, 27795): 150.39146984177776, (25, 27801): 149.32847336529022, (25, 27813): 152.10572643611758, (25, 27816): 151.55944959165114, (25, 27823): 149.29732413500676, (25, 27830): 150.8905729579169, (25, 27884): 118.41024823252918, (25, 27885): 124.03647896813382, (25, 27896): 120.67377901891079, (25, 27919): 120.51101467707025, (25, 27922): 121.10875590102509, (25, 27930): 119.35423100689094, (25, 27934): 119.50818123370844, (25, 27935): 119.59720051692423, (25, 27948): 143.16738270847662, (25, 27951): 145.1671119836501, (25, 28061): 119.39929818704795, (25, 28290): 163.3723845593945, (25, 28292): 164.11039038321533, (25, 28293): 163.50308863825413, (25, 28295): 163.0270933990676, (25, 28296): 163.27298618828786, (25, 28297): 162.9708782133587, (25, 28302): 162.56173525002163, (25, 28310): 175.79455699096567, (25, 28313): 176.5333616214822, (25, 28372): 176.53857763710542, (25, 28398): 176.6165594858722, (25, 28399): 176.33743475671724, (25, 28400): 176.80418647306792, (25, 28401): 175.5658190584281, (25, 28445): 176.14761089542642, (25, 28475): 174.5603358009224, (25, 28885): 62.25420288901576, (25, 28886): 61.84959705712061, (25, 28915): 62.18927633193368, (25, 28916): 61.8508467826581, (25, 28917): 61.63576464992525, (25, 28921): 63.00421997061881, (25, 28931): 62.88830220091264, (25, 28945): 60.996622366496005, (25, 28982): 61.41334380959225, (25, 29219): 64.23719524139923, (25, 29228): 62.44300916464489, (25, 29246): 74.61598788643163, (25, 29248): 74.70096853576517, (25, 29282): 72.20477401864736, (25, 29290): 75.58150223196012, (25, 29291): 75.15200457241585, (25, 29292): 75.58458872999235, (25, 29293): 74.62337034123007, (25, 29294): 75.48071072063382, (25, 29298): 74.75314964637276, (25, 29299): 74.73046543298473, (25, 29304): 73.70328197410481, (25, 29317): 71.32586975609453, (25, 29323): 71.13548742353542, (25, 29330): 72.28933081120175, (25, 29331): 72.81717925559204, (25, 29344): 64.8574687832504, (25, 29445): 45.9795986693425, (25, 29724): 242.27431930353657, (25, 29738): 242.62814820349445, (25, 29745): 241.59316466363902, (25, 29748): 241.78560143825536, (25, 29750): 242.3601491742246, (25, 29759): 241.30171965150413, (25, 29772): 242.6091686651047, (25, 29781): 242.32343983626566, (25, 29784): 242.10413493374747, (25, 29790): 242.60642402231124, (25, 29811): 241.85861177630525, (25, 29817): 244.26907900085143, (25, 29818): 243.9914974792713, (25, 29929): 241.47850540521728, (25, 30039): 246.1475188101405, (25, 30066): 243.20861863356012, (25, 30116): 231.10716565032627, (25, 30238): 213.22742183539367, (25, 30248): 222.05414492223642, (25, 30260): 222.2591700436688, (25, 30545): 56.27500132646841, (25, 30733): 37.35108133734685, (25, 30756): 31.943217514008232, (25, 30921): 41.20115779911265, (25, 31079): 37.16667450525748, (25, 31149): 31.521354336990132, (25, 31154): 32.47286553105567, (25, 31160): 31.406973970186687, (25, 31163): 32.48599123684022, (25, 31189): 32.034389316012884, (25, 31215): 32.794123415861065, (25, 31259): 36.96901681249191, (25, 31262): 36.79277955054723, (25, 31430): 40.172418898235094, (25, 31568): 49.63817589586707, (25, 31751): 39.068063706334506, (27, 109): 75.14934462225526, (27, 872): 135.16602773912618, (27, 873): 136.04918189975538, (27, 877): 135.69555382759063, (27, 879): 135.82453417469688, (27, 884): 134.88862401742637, (27, 889): 135.4528975435834, (27, 891): 134.60154430607625, (27, 892): 136.51424216740526, (27, 894): 136.41153070610662, (27, 896): 135.59832918297124, (27, 903): 135.70419575362402, (27, 909): 134.27495271404487, (27, 910): 134.65092661981785, (27, 912): 134.06233831078174, (27, 913): 133.40527857657153, (27, 916): 133.16177870641187, (27, 926): 134.97081340232592, (27, 927): 134.6802742834184, (27, 948): 134.2844309944237, (27, 961): 134.88540774142652, (27, 962): 135.00122776953165, (27, 963): 135.1264998802493, (27, 967): 136.08667062885863, (27, 974): 135.56413538233366, (27, 998): 136.4196335383132, (27, 1014): 156.00786169849584, (27, 1086): 133.89511604502997, (27, 1087): 133.92821386768685, (27, 1089): 133.0503647008924, (27, 1090): 133.40509874989147, (27, 1092): 134.65870535545838, (27, 1097): 133.67453579813875, (27, 1107): 135.37235698512094, (27, 1387): 39.500425309632014, (27, 1554): 40.42190026567769, (27, 1827): 175.7809298367645, (27, 1828): 175.8755315472089, (27, 1829): 176.01477973216623, (27, 1830): 175.87885528015977, (27, 1831): 175.95841182367607, (27, 1832): 175.86047777877613, (27, 1833): 175.87012230989214, (27, 1836): 175.76473035605065, (27, 1841): 176.34499555746723, (27, 1843): 176.1026023922601, (27, 1844): 176.21183060788798, (27, 1845): 175.9243883894052, (27, 1847): 174.98664274919207, (27, 1848): 175.30864001317892, (27, 1849): 176.81990205160932, (27, 1850): 176.97674001723755, (27, 1851): 175.55851969920656, (27, 1852): 175.58552220146285, (27, 1854): 175.73713662884907, (27, 1856): 174.94449723943762, (27, 1857): 175.2881492705803, (27, 1858): 176.67076880776656, (27, 1861): 175.9966169344644, (27, 1866): 174.926678846706, (27, 1867): 176.35928522587844, (27, 1868): 176.16267405379884, (27, 1870): 176.1895189298751, (27, 1871): 176.31318327307835, (27, 1875): 175.7185974510582, (27, 1880): 175.14363436670993, (27, 1882): 175.24320031838715, (27, 1883): 176.98559835520248, (27, 1889): 175.30772572040925, (27, 1893): 176.02891564967769, (27, 1894): 175.80100597807262, (27, 1899): 175.105718388394, (27, 1900): 175.27268641495198, (27, 1902): 176.42353308922512, (27, 1905): 176.7183107523042, (27, 1907): 175.52495177759215, (27, 1910): 175.63046096346818, (27, 1917): 177.3299520864107, (27, 1920): 175.54497677679043, (27, 1935): 176.75470463608877, (27, 1937): 177.00518074147848, (27, 1946): 174.59716645400852, (27, 1949): 174.87606262321358, (27, 1950): 173.89797844374303, (27, 1951): 174.37062221178232, (27, 1952): 174.73111429560288, (27, 1953): 174.87963381736577, (27, 1954): 174.6602550322775, (27, 1958): 174.79801400844855, (27, 1960): 175.27400515359247, (27, 1968): 175.46193020504137, (27, 1969): 176.8092689527785, (27, 1974): 176.45702607982668, (27, 1975): 176.45449552478027, (27, 1979): 175.77800793079297, (27, 1980): 175.72883319742468, (27, 1981): 175.923317799871, (27, 1985): 176.08464042109625, (27, 1994): 173.5302075638402, (27, 2011): 175.23413340792388, (27, 2019): 177.60794980964008, (27, 2020): 177.29376698553938, (27, 2029): 176.11244586504924, (27, 2030): 177.0758799217007, (27, 2032): 175.9253681579106, (27, 2033): 176.54695138337962, (27, 2034): 176.54199679205382, (27, 2036): 175.38658441627467, (27, 2037): 175.68069460626842, (27, 2038): 175.75346311508184, (27, 2042): 179.35713464626443, (27, 2050): 176.3767414910062, (27, 2051): 176.33057847506294, (27, 2053): 176.42359253573005, (27, 2054): 176.742528501942, (27, 2066): 176.09454149941223, (27, 2067): 176.0936875143523, (27, 2071): 172.92786070977414, (27, 2072): 173.52089647699302, (27, 2073): 171.8770003205561, (27, 2074): 171.79811525213952, (27, 2080): 170.7970827077113, (27, 2082): 173.8416439558986, (27, 2083): 174.14806187797416, (27, 2089): 173.49119099267722, (27, 2090): 173.77649819343267, (27, 2092): 173.3823612795703, (27, 2098): 171.1776191898229, (27, 2099): 171.52662201890473, (27, 2101): 171.1182172794517, (27, 2102): 172.73892679272655, (27, 2103): 172.23077042884356, (27, 2104): 171.95467223587863, (27, 2106): 174.35805050443975, (27, 2112): 171.33714152774456, (27, 2113): 172.97183504776024, (27, 2114): 173.36936000565922, (27, 2117): 174.6054003582434, (27, 2123): 172.2802161094992, (27, 2124): 172.61465868030885, (27, 2134): 171.64550687797842, (27, 2138): 172.63574535756652, (27, 2141): 171.766140947594, (27, 2148): 172.21108775083226, (27, 2150): 170.94930530126751, (27, 2151): 171.29704052283634, (27, 2152): 170.76044556540015, (27, 2153): 172.32676472922077, (27, 2154): 170.94331534289782, (27, 2155): 170.7787650296472, (27, 2156): 170.52450337066347, (27, 2157): 170.8631885690995, (27, 2160): 173.07754308626403, (27, 2161): 170.6972958262733, (27, 2162): 172.37572449432946, (27, 2163): 171.90665261344586, (27, 2164): 171.87409875840854, (27, 2168): 171.05871830519476, (27, 2172): 171.3554424150208, (27, 2174): 171.24975992114662, (27, 2178): 171.62657287288738, (27, 2179): 171.4094993617695, (27, 2183): 172.60603625111028, (27, 2185): 172.62363936630263, (27, 2186): 172.3585118418214, (27, 2190): 173.14820045118384, (27, 2192): 172.6693900023189, (27, 2193): 172.70178421743688, (27, 2194): 172.21303792470442, (27, 2195): 172.13476623847606, (27, 2197): 172.77113007448997, (27, 2205): 172.07817657192982, (27, 2207): 171.17889319638246, (27, 2208): 171.68074800535533, (27, 2212): 172.86271028604747, (27, 2214): 162.88827610241788, (27, 2225): 164.0622415723106, (27, 2231): 161.88761164691294, (27, 2278): 168.96392240686924, (27, 2284): 169.98334592279937, (27, 2285): 169.84559275457607, (27, 2291): 167.8656850069907, (27, 2292): 168.05129619671948, (27, 2307): 169.32639394611152, (27, 2313): 167.64151080336646, (27, 2317): 167.29550992075121, (27, 2319): 168.40195086435904, (27, 2321): 168.87126429406956, (27, 2323): 168.80232053378637, (27, 2326): 170.55998110509705, (27, 2327): 170.1221328806344, (27, 2329): 169.82378326822803, (27, 2330): 169.48510366691724, (27, 2332): 170.2092080549549, (27, 2344): 169.08553087771088, (27, 2346): 169.06806984300428, (27, 2361): 168.89329423582686, (27, 2368): 173.9945763405839, (27, 2374): 174.4781880307907, (27, 2375): 174.63811128260835, (27, 2377): 172.95483231644127, (27, 2378): 174.94270289339374, (27, 2379): 174.9880862145282, (27, 2380): 175.1520786339121, (27, 2383): 173.40261429107017, (27, 2385): 173.66184036245915, (27, 2395): 173.69005512226346, (27, 2397): 174.7895144334871, (27, 2398): 172.41895135313732, (27, 2399): 173.02341906829886, (27, 2400): 172.88773137482954, (27, 2402): 173.85413871029098, (27, 2403): 174.23051638570143, (27, 2404): 174.3262949598611, (27, 2405): 173.42035602323125, (27, 2407): 174.1568516742223, (27, 2408): 174.59955370263933, (27, 2409): 173.69474664973737, (27, 2411): 174.23345203816405, (27, 2412): 174.13232278404314, (27, 2413): 174.4420865546571, (27, 2414): 173.94062308078932, (27, 2422): 174.12109478847296, (27, 2424): 174.23737718159856, (27, 2426): 174.31786984937492, (27, 2433): 173.6182008737723, (27, 2436): 173.43528841780363, (27, 2437): 171.2359622714316, (27, 2440): 171.71967323020704, (27, 2445): 181.52553640522544, (27, 2447): 180.3154041147574, (27, 2454): 181.444952481576, (27, 2455): 181.50010598104674, (27, 2460): 178.0031165165865, (27, 2461): 178.4363038890677, (27, 2471): 185.4891258155419, (27, 2492): 178.6792376961263, (27, 2511): 175.00756529972733, (27, 2523): 176.88551912139673, (27, 2525): 176.39851190681048, (27, 2535): 176.94501344424341, (27, 2537): 176.1761167135224, (27, 2538): 176.69346940305317, (27, 2539): 176.5348047267843, (27, 2540): 177.2955166997429, (27, 2542): 177.87561828856198, (27, 2559): 188.77956356847255, (27, 2575): 187.8527398135989, (27, 2599): 171.03374156796932, (27, 2600): 174.78919638447059, (27, 2607): 172.59626589311264, (27, 2627): 177.56571802176848, (27, 2647): 179.71898655689475, (27, 2674): 178.52111098976943, (27, 2681): 178.29838547716315, (27, 2683): 179.27737330524525, (27, 2686): 178.08855277411448, (27, 2689): 191.60266567010618, (27, 2690): 191.68488394556397, (27, 2713): 194.8648219385898, (27, 2714): 195.18052810162743, (27, 2715): 195.5077963492946, (27, 2739): 195.19105539561465, (27, 2740): 192.88468796034667, (27, 2741): 193.03120063037687, (27, 2749): 194.83446248977182, (27, 2750): 194.90437523803436, (27, 2752): 195.12320221532607, (27, 2755): 195.40259590137885, (27, 2758): 195.35433798243727, (27, 2759): 195.34082639010157, (27, 2769): 194.92339577526369, (27, 2771): 193.47494214097546, (27, 2779): 193.80526756477553, (27, 2784): 190.21383646557155, (27, 2800): 191.1225213042612, (27, 2802): 192.36718223659904, (27, 2803): 192.21412063614744, (27, 2804): 191.98355451487555, (27, 2805): 192.73027511308857, (27, 2807): 192.6805305533369, (27, 2809): 192.62385235958226, (27, 2812): 190.4407180849702, (27, 2814): 192.71453639963767, (27, 2817): 193.07610585413255, (27, 2819): 192.65285884845693, (27, 2823): 190.90618682710257, (27, 2832): 193.18036054090274, (27, 2836): 191.69596613409686, (27, 2839): 192.6463902787874, (27, 2841): 193.00031952748094, (27, 2843): 192.83876049344084, (27, 2846): 192.11058166810363, (27, 2849): 193.46232072037822, (27, 2852): 193.1060611043123, (27, 2853): 193.62818924047747, (27, 2876): 193.92122036468285, (27, 2877): 195.13336897499144, (27, 2885): 195.80152107847556, (27, 2918): 192.64326578109788, (27, 2921): 193.18848060301573, (27, 2925): 190.54887005285468, (27, 2926): 189.62596316209402, (27, 2930): 191.8574988229529, (27, 2931): 190.84158842241936, (27, 2938): 192.697419063222, (27, 2940): 193.96885353578222, (27, 2947): 192.16095835337373, (27, 2949): 191.73369012643607, (27, 2950): 192.01118845928576, (27, 2952): 191.75920969921597, (27, 2958): 191.69043384318442, (27, 2959): 191.88079850542, (27, 2960): 192.46310026499575, (27, 2961): 192.2134646151538, (27, 2963): 191.50310417886703, (27, 2968): 191.69263350028237, (27, 2976): 191.40707319122984, (27, 2981): 186.9507114132256, (27, 2982): 186.87526446234716, (27, 2984): 186.6401408907593, (27, 3003): 186.27267783263378, (27, 3046): 182.324680334842, (27, 3050): 185.19988767386093, (27, 3051): 185.37509029939397, (27, 3053): 184.84853658951812, (27, 3069): 188.02867891404665, (27, 3071): 184.58303656600933, (27, 3080): 195.92576196826374, (27, 3199): 185.876048567036, (27, 3200): 185.34552754931846, (27, 3205): 188.87475482157507, (27, 3209): 185.65640859306723, (27, 3215): 185.34116773781466, (27, 3217): 184.63913079042976, (27, 3249): 185.36309582320283, (27, 3263): 190.64984568498542, (27, 3289): 186.92775608121528, (27, 3301): 187.19795382962099, (27, 3302): 186.90720342359094, (27, 3307): 186.5809793105111, (27, 3310): 187.50043412677712, (27, 3391): 190.46711619858445, (27, 3509): 71.25090385916411, (27, 3510): 70.7438924473387, (27, 3511): 71.01831503591627, (27, 3512): 70.65005881110555, (27, 3514): 70.70829696288776, (27, 3519): 72.76428035768718, (27, 3536): 72.03589454992037, (27, 3545): 72.77156611139671, (27, 3548): 71.91579664926684, (27, 3572): 72.3990898523935, (27, 3581): 72.00099003427962, (27, 3583): 71.39045235855635, (27, 3601): 73.82249249501568, (27, 3656): 73.28323018363494, (27, 3669): 72.97083508559294, (27, 3670): 73.45109068347605, (27, 3695): 70.58356306173177, (27, 3696): 70.92729954882323, (27, 3782): 71.28666512274127, (27, 3792): 70.82430341444011, (27, 3989): 149.29259096773959, (27, 4008): 152.03558528502674, (27, 4031): 151.83501266829987, (27, 4045): 150.88264329748213, (27, 4144): 151.05863241782396, (27, 4145): 148.34641371759344, (27, 4164): 150.00822926823326, (27, 4168): 149.1711173245724, (27, 4173): 149.00590936621344, (27, 4181): 147.33780977253963, (27, 4228): 145.7178471483047, (27, 4248): 145.09445250315034, (27, 4254): 130.49491401779568, (27, 4260): 130.51037512265955, (27, 4262): 131.49098410071653, (27, 4273): 131.25852851641116, (27, 4319): 122.44864555281166, (27, 4326): 122.14085412781448, (27, 4328): 122.2462363405286, (27, 4334): 122.84176003572324, (27, 4335): 122.6340197497511, (27, 4372): 123.7504191994704, (27, 4413): 132.82522197447904, (27, 4434): 123.28428921116468, (27, 4447): 124.13244875740703, (27, 4452): 123.45440690152927, (27, 4463): 107.9711287036214, (27, 4465): 108.40822823438289, (27, 4619): 134.83510961439518, (27, 4645): 136.48755364151012, (27, 4657): 136.32693520102572, (27, 4666): 135.73715588611793, (27, 4676): 136.99739594973153, (27, 4678): 137.21946406389873, (27, 4689): 136.51002155536585, (27, 4704): 142.79604288888143, (27, 4726): 160.42414686092624, (27, 4727): 160.1090465914254, (27, 4730): 159.49089964954902, (27, 4731): 159.7149057722639, (27, 4734): 159.795816776401, (27, 4735): 159.53680767059248, (27, 4736): 159.72131658480276, (27, 4737): 159.23860912033464, (27, 4738): 159.33702448662214, (27, 4756): 159.67309356460572, (27, 4760): 157.9034579565724, (27, 4761): 158.00687527448557, (27, 4762): 157.51893514672776, (27, 4765): 158.0807315775364, (27, 4773): 161.005692868439, (27, 4774): 160.78200525771783, (27, 4790): 160.78784023768986, (27, 4795): 160.49850095328532, (27, 4799): 160.94882070673424, (27, 4801): 161.68884183041033, (27, 4804): 160.5348268975238, (27, 4805): 160.29822570713964, (27, 4806): 160.74773737042682, (27, 4815): 160.49698416914063, (27, 4816): 161.2602557465921, (27, 4817): 161.48430825359006, (27, 4826): 160.99285512239075, (27, 4830): 160.57371353963836, (27, 4839): 158.82240178853715, (27, 4840): 159.13057806707812, (27, 4841): 158.4905278061118, (27, 4846): 158.26169279415404, (27, 4848): 158.2461060604573, (27, 4850): 158.5414912639691, (27, 4871): 154.6483627695174, (27, 4883): 157.46994995861075, (27, 4900): 155.94360403027397, (27, 4901): 155.59564439182455, (27, 4917): 135.79923261801682, (27, 4931): 133.56713776650741, (27, 4944): 136.00862635069467, (27, 4956): 134.02027774178904, (27, 4958): 134.04346051293928, (27, 4959): 133.68068828732552, (27, 4961): 134.43681310031488, (27, 4966): 133.52546856269453, (27, 5207): 131.06163339725882, (27, 5272): 86.44371575234656, (27, 5283): 87.25776866324225, (27, 5287): 88.6138952743457, (27, 5289): 88.97609053016035, (27, 5293): 86.56379310855606, (27, 5295): 88.82857501785692, (27, 5296): 88.83406879881636, (27, 5298): 88.82175233934738, (27, 5303): 89.52140945863168, (27, 5305): 86.0278675783571, (27, 5306): 85.4464063796784, (27, 5307): 85.60799096115517, (27, 5308): 86.41425697079474, (27, 5313): 86.33840629347424, (27, 5314): 86.84050902450424, (27, 5317): 86.44469094676005, (27, 5319): 88.74419565633006, (27, 5324): 88.26031759625745, (27, 5326): 87.95042090640946, (27, 5348): 85.29424565294475, (27, 5351): 85.97308035028759, (27, 5399): 89.50446862499682, (27, 5413): 87.16561218215611, (27, 5422): 89.90000370348628, (27, 5445): 88.05100996262944, (27, 5448): 87.27360793928194, (27, 5456): 87.13876690033531, (27, 5467): 87.87700645887062, (27, 5624): 79.26697520880974, (27, 5671): 104.09296790833133, (27, 5672): 103.04789113437752, (27, 5797): 116.64999275328412, (27, 5871): 101.37331582502094, (27, 5976): 92.07645282715755, (27, 6118): 138.2423759200282, (27, 6248): 151.59375862179735, (27, 6345): 52.48922251154399, (27, 6352): 51.00882418470541, (27, 6354): 52.71561639866802, (27, 6359): 53.2825856228411, (27, 6376): 51.93517490761249, (27, 6378): 52.56290574794532, (27, 6381): 53.34021306811079, (27, 6383): 52.06043133886835, (27, 6396): 54.25126692246144, (27, 6399): 52.83331559979471, (27, 6408): 50.77874566302518, (27, 6409): 50.766769664739364, (27, 6419): 47.2023911676411, (27, 6422): 50.39980773893776, (27, 6423): 50.238309813887604, (27, 6424): 51.7975046454465, (27, 6439): 51.27664721779724, (27, 6464): 50.62695692259609, (27, 6465): 50.702662972159445, (27, 6469): 51.39837756919718, (27, 6470): 51.4218013923133, (27, 6472): 53.91137381596415, (27, 6480): 52.47635302978645, (27, 6486): 52.403339016529884, (27, 6497): 52.355290270911496, (27, 6503): 49.448025132488894, (27, 6508): 50.243951721695346, (27, 6509): 50.2558018054651, (27, 6521): 52.20974295789297, (27, 6544): 51.46219202813802, (27, 6552): 49.445694545312044, (27, 6553): 49.123656654464895, (27, 6554): 48.805933794282495, (27, 6578): 50.08424715028048, (27, 6582): 49.16135479398149, (27, 6601): 50.081095297505364, (27, 6609): 53.261811849657704, (27, 6610): 53.20349918194274, (27, 6611): 53.63959602067735, (27, 6614): 53.71251615126494, (27, 6615): 53.63354583870522, (27, 6616): 53.459260398244766, (27, 6617): 53.49085525308394, (27, 6618): 53.45671039762712, (27, 6619): 53.418293728944874, (27, 6620): 53.23795555814901, (27, 6621): 52.932438695265326, (27, 6622): 53.15085532813862, (27, 6623): 53.42519545498645, (27, 6624): 52.95114664956285, (27, 6625): 53.030341919624064, (27, 6626): 53.50942515400147, (27, 6627): 53.861512773139935, (27, 6628): 52.95516760621416, (27, 6629): 52.73687963790629, (27, 6630): 53.19703856432183, (27, 6632): 52.838989167646005, (27, 6634): 52.76942229675243, (27, 6635): 52.962794321337775, (27, 6636): 53.39449051611846, (27, 6637): 52.357957031554264, (27, 6638): 52.998117305551595, (27, 6639): 53.746315007395985, (27, 6640): 53.16229932017105, (27, 6641): 52.74903595306252, (27, 6642): 52.84501640349652, (27, 6643): 53.65386313562494, (27, 6645): 53.34492054732987, (27, 6646): 53.540265584573895, (27, 6647): 53.009631240121806, (27, 6653): 53.695507169351316, (27, 6655): 53.827683438048, (27, 6658): 52.656105251751605, (27, 6662): 52.66111989990581, (27, 6819): 35.27864880685556, (27, 6996): 36.74222188359927, (27, 7059): 40.638152115486854, (27, 7187): 31.547787928413367, (27, 7304): 23.468416841909537, (27, 7528): 34.55132332394968, (27, 7720): 59.93935729913199, (27, 7793): 59.07600671148331, (27, 7807): 59.51819526104133, (27, 7808): 58.88675956488636, (27, 7831): 53.705210170070906, (27, 7850): 58.21500216325147, (27, 7852): 57.696741831698944, (27, 8012): 59.49334987212199, (27, 8125): 61.749669887912205, (27, 8208): 67.45812746262963, (27, 8392): 54.00021344157526, (27, 8651): 23.529589802443304, (27, 9088): 40.744839929026675, (27, 9443): 12.5, (27, 9444): 12.5, (27, 9828): 23.56285383405899, (27, 9868): 21.15488186072963, (27, 10180): 62.260414702478556, (27, 10256): 73.26164931234507, (27, 10276): 68.01298608446653, (27, 10378): 69.2456477818438, (27, 10676): 60.390055348025975, (27, 10714): 54.124288079465245, (27, 10730): 53.48981973742646, (27, 10862): 87.78432089922427, (27, 10881): 89.1688892263747, (27, 10883): 89.16536348907175, (27, 10885): 87.44940680357497, (27, 10891): 89.16807467409602, (27, 10909): 88.68675970609328, (27, 10911): 88.51375172981972, (27, 10913): 88.31164248670324, (27, 10915): 88.10758084882136, (27, 10919): 88.14257066231443, (27, 11037): 84.08857209032955, (27, 11039): 79.00587418084861, (27, 11516): 178.67154352855283, (27, 11856): 123.10396888647787, (27, 11857): 122.68592287313149, (27, 11861): 122.90862805820367, (27, 11881): 122.48031480386608, (27, 11902): 120.61130239265168, (27, 11911): 120.30285703412174, (27, 11914): 120.54870582771379, (27, 11922): 121.92732180606815, (27, 11924): 122.37514532881801, (27, 11926): 121.83859218770701, (27, 11950): 122.93584503880248, (27, 11963): 124.68846166011265, (27, 11983): 123.5531840883759, (27, 11985): 125.56525193672584, (27, 12009): 125.26511985918297, (27, 12010): 124.01091550603105, (27, 12018): 124.22210810872674, (27, 12020): 124.55275261266901, (27, 12021): 124.76375605336273, (27, 12024): 125.95197130462498, (27, 12025): 125.54114183468134, (27, 12027): 125.2619669451736, (27, 12031): 123.8026897014841, (27, 12032): 124.20893090405673, (27, 12035): 125.19723775423282, (27, 12041): 125.69541364487439, (27, 12045): 109.21168924006415, (27, 12145): 116.88615258962396, (27, 12275): 150.49069750210634, (27, 12294): 147.55455114962888, (27, 12358): 157.46376501811432, (27, 12463): 161.44886551962915, (27, 12465): 161.35057675011907, (27, 12482): 162.7963908279678, (27, 12503): 162.61659510611827, (27, 12506): 163.0595058627443, (27, 12549): 161.8697874335054, (27, 12559): 161.57667655750743, (27, 12569): 162.0215614996129, (27, 12572): 162.350065639121, (27, 12574): 161.63800407549263, (27, 12576): 162.22834909529627, (27, 12591): 162.02243497721, (27, 12608): 164.62969133580134, (27, 12696): 160.229407775937, (27, 12710): 162.60480726695943, (27, 12728): 161.53531532489762, (27, 12766): 88.97648393277152, (27, 12771): 84.69819912016403, (27, 12790): 84.28692885160028, (27, 12795): 83.4658504278857, (27, 12797): 78.56857924063459, (27, 12798): 79.1259238532696, (27, 12811): 82.63532410637163, (27, 12830): 81.63417861512463, (27, 12848): 81.89677185512822, (27, 12850): 81.99278193470424, (27, 12852): 81.36113675798886, (27, 12854): 80.82640017849548, (27, 12859): 82.34187716574415, (27, 12861): 79.63973348593724, (27, 12865): 83.4462293031117, (27, 12866): 83.06750878807011, (27, 12867): 84.2315432403699, (27, 12874): 83.68132123747704, (27, 12875): 84.0418099403196, (27, 12881): 82.50281828406291, (27, 12883): 83.15124182760123, (27, 12885): 84.41634652958078, (27, 12888): 82.77601421436812, (27, 12889): 82.55906556672424, (27, 12892): 83.83592385504214, (27, 12893): 82.8722492869616, (27, 12896): 83.11755532079708, (27, 12906): 84.04214974944459, (27, 13018): 81.66172456168142, (27, 13071): 82.32471680947955, (27, 13131): 75.89425030964362, (27, 13146): 78.88644326416434, (27, 13159): 77.27339846108704, (27, 13193): 75.07373353101904, (27, 13198): 68.19814783658117, (27, 13292): 74.87380738757867, (27, 13296): 76.08389808236493, (27, 13406): 66.19813153799421, (27, 13407): 66.15884511427606, (27, 13417): 66.98371193534997, (27, 13418): 67.80790415835733, (27, 13438): 69.32031780742575, (27, 13442): 69.42999988629427, (27, 13443): 68.9933585330992, (27, 13764): 53.308885556455046, (27, 13766): 53.45709903010155, (27, 13771): 54.368973030719374, (27, 13783): 51.42115479598657, (27, 13784): 53.175852841277255, (27, 13792): 55.71591218700687, (27, 13824): 51.535803122277606, (27, 14017): 46.53252562047932, (27, 14870): 80.4259468301638, (27, 14997): 28.58171098380036, (27, 15000): 28.81024810051341, (27, 15003): 29.437262938971998, (27, 15006): 29.78639767702348, (27, 15007): 30.2589181746902, (27, 15056): 30.62572328072543, (27, 15063): 30.31412615916072, (27, 15069): 30.363087125969233, (27, 15076): 30.421797130723682, (27, 15086): 28.81944699551808, (27, 15087): 28.498491818719973, (27, 15111): 26.989632127020933, (27, 15116): 27.86779099370344, (27, 15722): 15.58935594745622, (27, 15998): 19.590786028854705, (27, 16073): 109.88718227270621, (27, 16939): 147.4697468142253, (27, 16940): 146.7993502981035, (27, 16951): 147.6081850532988, (27, 16963): 147.66090951277675, (27, 16965): 148.45719162604024, (27, 16969): 148.28871648472887, (27, 16970): 147.94016880867318, (27, 16971): 147.22092197846166, (27, 16973): 147.1899444638705, (27, 16974): 148.7934090238891, (27, 16976): 147.98563801689968, (27, 16978): 147.4542925073171, (27, 16980): 148.2383190156206, (27, 16982): 148.80603899847895, (27, 17045): 173.9820323238906, (27, 17048): 174.91612331348267, (27, 17304): 141.19958696663286, (27, 17305): 140.74124642145676, (27, 17330): 141.18054243337875, (27, 17334): 140.29381778352555, (27, 17343): 141.86068729607524, (27, 17345): 140.2662434901604, (27, 17347): 141.1234332752381, (27, 17351): 139.06463686840098, (27, 17372): 140.19450098423852, (27, 17373): 141.806291775145, (27, 17377): 141.92015863683895, (27, 17382): 140.87170259269647, (27, 17383): 141.06432850774385, (27, 17389): 140.4461031439122, (27, 17400): 141.5122415634546, (27, 17401): 141.49045509311796, (27, 17402): 141.57484093226276, (27, 17403): 141.67990169846166, (27, 17440): 140.34122244058136, (27, 17455): 141.68339480526356, (27, 17491): 141.79270962614348, (27, 17507): 139.66949392006953, (27, 17509): 140.25407507495487, (27, 17590): 138.68002732936867, (27, 17615): 135.49795364166837, (27, 17642): 136.06954117089475, (27, 17643): 136.01030466276717, (27, 17668): 135.48084439654988, (27, 17721): 134.18171084760348, (27, 17754): 139.69445374210028, (27, 17769): 139.87509376302225, (27, 17776): 137.53559919852503, (27, 17804): 140.8246694636578, (27, 17809): 141.40998337314315, (27, 17824): 141.03861876485018, (27, 17837): 139.30796319906415, (27, 17838): 139.3695310561221, (27, 17862): 138.9334744192561, (27, 17866): 140.18030056774938, (27, 17872): 138.51388292510532, (27, 17873): 137.56092924227218, (27, 17881): 139.02291342455845, (27, 17947): 93.72117238136815, (27, 17951): 92.4242187596482, (27, 17953): 92.20570548454238, (27, 17954): 92.31617943706237, (27, 17959): 93.4049925159528, (27, 17963): 92.90247430205115, (27, 18000): 86.40691095916205, (27, 18001): 86.69558175110551, (27, 18111): 107.45293637995714, (27, 18148): 74.97014982424008, (27, 18166): 88.0153301209652, (27, 18189): 99.19413872870615, (27, 18239): 142.10175500758808, (27, 18240): 142.09201204203075, (27, 18245): 142.15515095472912, (27, 18247): 142.0238921803565, (27, 18251): 142.14962534996133, (27, 18256): 142.2828268154334, (27, 18258): 142.13410650218376, (27, 18259): 142.1592287560358, (27, 18260): 142.2144620030391, (27, 18262): 142.32139348724476, (27, 18263): 142.3199552096304, (27, 18264): 142.37503376206976, (27, 18266): 142.36283377390205, (27, 18267): 142.41719089500018, (27, 18268): 142.4430261783511, (27, 18269): 142.55121068979412, (27, 18275): 142.50014831980417, (27, 18285): 142.35732135086167, (27, 18308): 141.22723771500426, (27, 18313): 140.83651970391995, (27, 18314): 141.0045991403521, (27, 18315): 142.55233730128478, (27, 18316): 142.5400004279075, (27, 18317): 142.59037811913538, (27, 18320): 142.64251868079242, (27, 18321): 142.6687247746585, (27, 18322): 142.74878154645882, (27, 18324): 142.8186134770268, (27, 18325): 143.0720501411095, (27, 18326): 142.97777552232583, (27, 18327): 142.63391752134746, (27, 18329): 143.1895290508514, (27, 18330): 143.05292692980734, (27, 18331): 142.8847679123696, (27, 18332): 142.70999051208693, (27, 18333): 143.02923503708064, (27, 18336): 142.89178865064724, (27, 18337): 142.9799911790001, (27, 18403): 142.83429298833292, (27, 18432): 139.31771654346193, (27, 18451): 141.69607064455107, (27, 18466): 144.03835554576017, (27, 18481): 142.62706496128632, (27, 18483): 142.62471827423653, (27, 18484): 142.48704283291283, (27, 18485): 142.0751673428141, (27, 18486): 142.45695055272247, (27, 18487): 142.1358179277653, (27, 18489): 142.41041059172912, (27, 18490): 142.7398781794253, (27, 18491): 142.89241332598056, (27, 18492): 141.8080217199104, (27, 18493): 142.40545267344893, (27, 18494): 142.3466408338336, (27, 18495): 142.6265509288385, (27, 18496): 142.46484833510274, (27, 18497): 142.06404095595596, (27, 18498): 142.12918065645684, (27, 18499): 142.36595452653057, (27, 18501): 142.19847735437796, (27, 18502): 142.04729547842152, (27, 18503): 141.9285768397585, (27, 18504): 142.52532084161504, (27, 18506): 142.2275677380717, (27, 18507): 142.08479183118237, (27, 18508): 142.33506534493327, (27, 18509): 142.34015574222448, (27, 18510): 141.93555768172686, (27, 18511): 142.45569451778286, (27, 18512): 142.27263174599085, (27, 18515): 142.54268012789157, (27, 18516): 142.56171473024244, (27, 18517): 142.37405244994386, (27, 18518): 142.68481315319994, (27, 18519): 142.55688568066537, (27, 18520): 142.2877389137581, (27, 18522): 143.19714824644336, (27, 18523): 143.2320764917328, (27, 18532): 143.4456003891829, (27, 18535): 143.00399992555148, (27, 18537): 142.7581290676767, (27, 18539): 142.8105211138392, (27, 18540): 142.8401873622292, (27, 18541): 142.96209958034444, (27, 18542): 143.0393275831417, (27, 18543): 142.6564825211303, (27, 18546): 142.8415806554989, (27, 18555): 143.2272795494461, (27, 18556): 143.29878424301063, (27, 18565): 143.41946821940482, (27, 18567): 143.535790683631, (27, 18568): 143.32391074724148, (27, 18577): 144.8318085020302, (27, 18583): 144.5738481496097, (27, 18605): 144.88534973632187, (27, 18608): 143.6732153669878, (27, 18616): 146.2928879078208, (27, 18618): 147.49362481739286, (27, 18625): 147.07310767503878, (27, 18645): 146.0110322518449, (27, 18646): 146.28987403202942, (27, 18653): 145.2991568607459, (27, 18654): 146.26411424956524, (27, 18655): 145.6321740307022, (27, 18666): 149.50866978333394, (27, 18837): 145.45602179530957, (27, 18974): 141.68446241032586, (27, 18999): 142.7094987381286, (27, 19000): 143.0714149524084, (27, 19174): 126.42334208264758, (27, 19342): 133.96335047744805, (27, 19455): 128.64711402704404, (27, 19555): 111.42048042689345, (27, 19564): 113.10371722266008, (27, 19573): 112.20038913129103, (27, 19586): 111.75612618918241, (27, 19605): 111.9412100938897, (27, 19611): 112.52488765155232, (27, 19614): 112.09059063120664, (27, 19641): 121.07349137222907, (27, 19702): 121.10902210988414, (27, 19713): 120.41170606977937, (27, 19731): 107.66736594403483, (27, 19819): 126.19942228428934, (27, 19893): 105.22314089862489, (27, 19899): 109.4930657572832, (27, 19929): 106.29627666544573, (27, 19951): 114.62202983975752, (27, 19962): 107.06187717290263, (27, 19970): 108.72166419137453, (27, 19971): 108.79404157466416, (27, 19972): 108.12117062904282, (27, 19975): 107.7669087655308, (27, 19978): 116.21256561609736, (27, 19987): 116.33581335745636, (27, 19989): 114.05322960088519, (27, 20039): 116.74700067120827, (27, 20043): 117.67708749198908, (27, 20047): 116.92861415319281, (27, 20052): 114.42418816931891, (27, 20054): 114.63203882595181, (27, 20085): 125.93982821929764, (27, 20104): 126.65004923897997, (27, 20132): 122.31673450478623, (27, 20203): 105.22120903238732, (27, 20280): 104.46672823908665, (27, 20285): 104.31471911302813, (27, 20290): 104.83250768314419, (27, 20297): 104.0315726320131, (27, 20309): 117.08461432334322, (27, 20453): 128.74239019272312, (27, 20485): 99.02770262842616, (27, 20520): 97.00616627283149, (27, 20526): 96.43764662481027, (27, 20698): 70.93235125434188, (27, 20868): 80.0886590896777, (27, 21042): 79.58529012393375, (27, 21057): 84.42904343404248, (27, 21066): 81.97890038068606, (27, 21075): 81.18008040056007, (27, 21093): 79.84974501966593, (27, 21098): 83.16014823581617, (27, 21127): 79.92838090658063, (27, 21130): 80.79384814406772, (27, 21144): 80.75133929369647, (27, 21146): 79.61278594783649, (27, 21147): 80.70175196045534, (27, 21148): 81.50498392286653, (27, 21153): 80.01089830069637, (27, 21293): 87.46387655694507, (27, 21426): 87.72229965258926, (27, 21442): 93.2640422577645, (27, 21451): 93.78924060719639, (27, 21466): 90.3628444368683, (27, 21469): 91.08047192832203, (27, 21471): 90.0037102629104, (27, 21473): 90.57141284290398, (27, 21475): 90.03546446490716, (27, 21482): 91.61714920130937, (27, 21484): 91.42371976257677, (27, 21488): 91.0259380602417, (27, 21494): 89.91608441282806, (27, 21498): 90.48077635978798, (27, 21500): 89.4986924140169, (27, 21514): 90.61743587164351, (27, 21537): 89.10206274678548, (27, 21662): 91.04962366735082, (27, 21691): 88.10992016587502, (27, 21757): 83.6845397311556, (27, 21777): 70.04201751478075, (27, 21778): 69.29606037439338, (27, 21779): 69.69321242179919, (27, 21790): 70.9080009985662, (27, 21802): 70.82506661023456, (27, 21824): 71.58462304609418, (27, 21874): 69.86884027530415, (27, 21879): 69.41522665299358, (27, 21983): 72.82222799251447, (27, 22002): 80.63950405979143, (27, 22132): 77.07283297645368, (27, 22261): 39.28521062170466, (27, 22298): 39.15972955925817, (27, 22339): 48.792337558613966, (27, 22508): 28.72346212174942, (27, 22841): 194.74324341448505, (27, 22842): 194.68325649176518, (27, 22874): 192.69057791349465, (27, 22941): 193.08840198841045, (27, 22956): 194.11789979554385, (27, 22960): 194.5903205369514, (27, 22968): 194.8028502441439, (27, 22970): 195.2225059348125, (27, 22974): 195.23080406866669, (27, 22980): 196.53066539617694, (27, 23025): 195.66218884467983, (27, 23028): 195.2218731133116, (27, 23081): 196.54581023443137, (27, 23104): 193.0607000936185, (27, 23147): 183.487259728273, (27, 23298): 103.0929097603224, (27, 23376): 100.93299908372582, (27, 23381): 99.38434981895851, (27, 23529): 104.2531565186423, (27, 23556): 103.03675539754435, (27, 23718): 102.0274525832227, (27, 24001): 115.93210491786716, (27, 24094): 119.49730550841332, (27, 24129): 121.63392653843245, (27, 24174): 117.07825694194878, (27, 24235): 121.75353678402367, (27, 24259): 123.85682894114744, (27, 24260): 123.69335881038597, (27, 24261): 123.24581008929137, (27, 24305): 126.32111694240162, (27, 24306): 126.71829996495389, (27, 24307): 126.10568863592229, (27, 24308): 121.60117934269276, (27, 24498): 131.96488681483817, (27, 24499): 132.0045058846047, (27, 24500): 131.61779772604834, (27, 24668): 129.37783226432296, (27, 24711): 134.49149919869265, (27, 24756): 135.84850033835284, (27, 24788): 136.48406995357252, (27, 24809): 134.0657819163898, (27, 24813): 134.82137854351595, (27, 24821): 134.57382381333124, (27, 24825): 134.75307582789722, (27, 24832): 133.90522851959528, (27, 24833): 134.27098995361243, (27, 24835): 134.63431678892968, (27, 24837): 135.21906999443675, (27, 24840): 133.84757073632684, (27, 24841): 134.41503099017825, (27, 24844): 133.86294838985413, (27, 24845): 134.20185410025326, (27, 24846): 134.16244237631923, (27, 24849): 134.36110769047318, (27, 24850): 134.93093796043613, (27, 24863): 129.8532300274731, (27, 24866): 130.50762842655607, (27, 24885): 131.27826009634015, (27, 24886): 131.33249614390002, (27, 24889): 132.777587623046, (27, 24903): 133.34057238110208, (27, 24909): 130.96184150733467, (27, 24999): 159.61652338140684, (27, 25019): 158.91406314066802, (27, 25028): 159.212436342415, (27, 25137): 107.26177230166245, (27, 25145): 108.0419039169657, (27, 25208): 118.45941762668248, (27, 25233): 117.45791149489271, (27, 25371): 106.47530394645804, (27, 25377): 103.98340260155636, (27, 25828): 62.8480519256681, (27, 25851): 55.76745031013959, (27, 25874): 61.902104526128426, (27, 25898): 65.45590794235014, (27, 25946): 62.16386992545011, (27, 26047): 76.81046770284132, (27, 26066): 88.27252525605714, (27, 26197): 79.90160860996119, (27, 26212): 49.587337219774724, (27, 26253): 48.69187823222154, (27, 26254): 48.83018142682844, (27, 26257): 49.756087855053885, (27, 26258): 49.04422618099098, (27, 26260): 49.36204196103474, (27, 26266): 47.61682317193485, (27, 26267): 48.221546207411365, (27, 26271): 48.40645665674582, (27, 26304): 51.7115073899582, (27, 26305): 51.302394982022975, (27, 26363): 62.2132110179562, (27, 26441): 57.492626149578285, (27, 26442): 57.096267516980376, (27, 26450): 56.34856226309522, (27, 26459): 57.27624639227843, (27, 26462): 57.81757005112972, (27, 26467): 60.17457657126298, (27, 26471): 59.014208308700965, (27, 26472): 58.80048727851796, (27, 26473): 58.63521719197349, (27, 26476): 56.83849296219413, (27, 26485): 57.179782181115975, (27, 26493): 56.700762169112636, (27, 26524): 58.60588160105887, (27, 26525): 58.24411782739811, (27, 26556): 58.7378705058658, (27, 26560): 59.472175925937734, (27, 26561): 59.1580398128117, (27, 26564): 58.29754330262835, (27, 26569): 58.76428421415251, (27, 26570): 58.25073205380195, (27, 26573): 57.94185903220251, (27, 26581): 57.53776453997839, (27, 26583): 57.60191140271109, (27, 26593): 57.057677839339945, (27, 26837): 59.95545799066081, (27, 26844): 60.68792286154968, (27, 26863): 58.17781547245879, (27, 26893): 59.93126107004186, (27, 26902): 60.910477648522935, (27, 26905): 60.72155402585919, (27, 26912): 61.22627185546803, (27, 26921): 59.068931435842785, (27, 26922): 55.83697276989217, (27, 27212): 83.60144244244874, (27, 27218): 83.75620645748704, (27, 27239): 84.55147256134244, (27, 27257): 83.66253078034913, (27, 27274): 84.61447846050639, (27, 27279): 84.15875141701287, (27, 27282): 83.50796025867744, (27, 27283): 84.40259023645153, (27, 27285): 84.71495779044288, (27, 27286): 83.54449960868001, (27, 27290): 82.9010524640126, (27, 27295): 82.99943695635906, (27, 27300): 84.85619522120616, (27, 27344): 81.63238350134462, (27, 27366): 82.04733167333384, (27, 27383): 84.08916874842932, (27, 27398): 85.68672928138119, (27, 27406): 85.26926082479613, (27, 27407): 85.72393872502677, (27, 27426): 87.09480300334232, (27, 27432): 83.6666397887189, (27, 27460): 86.11257798687149, (27, 27523): 77.20726307844475, (27, 27545): 95.12404366484938, (27, 27602): 110.09362044471291, (27, 27606): 110.72153185976269, (27, 27646): 87.93002327290104, (27, 27667): 91.10716188874665, (27, 27672): 91.48132483723607, (27, 27674): 90.80707921445384, (27, 27688): 92.07939604850463, (27, 27692): 91.80262502976207, (27, 27693): 91.27784202934427, (27, 27705): 91.01934345486094, (27, 27712): 91.08150749905883, (27, 27786): 118.70444828422231, (27, 27790): 119.65322027369024, (27, 27791): 119.9088920559082, (27, 27795): 117.5444672174308, (27, 27801): 117.99563272458587, (27, 27813): 118.89855496540663, (27, 27816): 118.84493680090118, (27, 27823): 118.03914135030388, (27, 27830): 118.75732142548482, (27, 27884): 80.227885135017, (27, 27885): 86.23593365193032, (27, 27896): 82.73542916790653, (27, 27919): 82.73060561009558, (27, 27922): 83.12481240677089, (27, 27930): 81.44909064015425, (27, 27934): 81.46513833463422, (27, 27935): 81.39105331123642, (27, 27948): 98.85954771139363, (27, 27951): 102.83542755022654, (27, 28061): 62.879575925872054, (27, 28290): 108.15611210133918, (27, 28292): 108.59932183002839, (27, 28293): 108.20441939081898, (27, 28295): 107.53871855948258, (27, 28296): 107.95431105270296, (27, 28297): 107.89484225690639, (27, 28302): 107.31001294836514, (27, 28310): 119.57476787822999, (27, 28313): 120.6025070931965, (27, 28372): 120.04225032930529, (27, 28398): 120.15961252289982, (27, 28399): 119.91987279162436, (27, 28400): 120.39384327128994, (27, 28401): 119.06812348851737, (27, 28445): 120.40458639422334, (27, 28475): 117.68109500755482, (27, 28885): 121.00458637390133, (27, 28886): 120.57072629020566, (27, 28915): 120.79712631150868, (27, 28916): 120.49453664628538, (27, 28917): 120.25083401958939, (27, 28921): 121.78158849346524, (27, 28931): 121.6384415814266, (27, 28945): 119.26946158187195, (27, 28982): 119.86894968430533, (27, 29219): 121.70887561948003, (27, 29228): 119.92769311842623, (27, 29246): 131.37903023058408, (27, 29248): 131.195121902055, (27, 29282): 128.79497762703957, (27, 29290): 132.58848229862136, (27, 29291): 132.09777220441592, (27, 29292): 132.55233342480147, (27, 29293): 131.61515627914966, (27, 29294): 132.34701011865897, (27, 29298): 131.67711683129357, (27, 29299): 131.58839671488792, (27, 29304): 130.73264361981091, (27, 29317): 128.4995164930687, (27, 29323): 128.3276323708584, (27, 29330): 129.40079167470913, (27, 29331): 129.9432402814371, (27, 29344): 121.8131250851139, (27, 29445): 101.24811788543563, (27, 29724): 194.1001155582609, (27, 29738): 194.43863108762878, (27, 29745): 193.54492310924027, (27, 29748): 194.22251457458773, (27, 29750): 194.98134584844925, (27, 29759): 193.69923763013244, (27, 29772): 194.9564537402878, (27, 29781): 194.69591974572774, (27, 29784): 194.2727888489766, (27, 29790): 195.05548602820826, (27, 29811): 194.55831390211262, (27, 29817): 198.2013417186135, (27, 29818): 197.95871638463092, (27, 29929): 193.13148907977504, (27, 30039): 196.31087763419052, (27, 30066): 192.76200555203033, (27, 30116): 182.1247431184058, (27, 30238): 166.6121670340649, (27, 30248): 172.81643255239302, (27, 30260): 172.87649120896603, (27, 30545): 115.28017565519002, (27, 30733): 96.38156959512693, (27, 30756): 90.68807198464712, (27, 30921): 100.16621736959449, (27, 31079): 62.093010318957546, (27, 31149): 57.110534934259434, (27, 31154): 57.567200138333845, (27, 31160): 56.91272908403355, (27, 31163): 57.26911806705899, (27, 31189): 48.52454682939109, (27, 31215): 49.44090664343973, (27, 31259): 50.55447911417379, (27, 31262): 49.50230412008566, (27, 31430): 64.24682759387586, (27, 31568): 47.77555407108617, (27, 31751): 58.87774497905097, (28, 109): 209.42688115292592, (28, 872): 33.381957881967466, (28, 873): 32.846140317472155, (28, 877): 32.61137757000893, (28, 879): 32.48953388159131, (28, 884): 32.07777686979766, (28, 889): 31.933026335155052, (28, 891): 32.3790226256319, (28, 892): 32.16997568636584, (28, 894): 32.414835279336266, (28, 896): 33.646267969298314, (28, 903): 32.096736264513744, (28, 909): 34.44351728233343, (28, 910): 34.62198463251475, (28, 912): 34.892181918364265, (28, 913): 35.054134759034014, (28, 916): 35.70070403964348, (28, 926): 34.972214379957784, (28, 927): 35.24202213259032, (28, 948): 32.653844624461264, (28, 961): 34.05290450127839, (28, 962): 34.271028663089574, (28, 963): 34.42712550856538, (28, 967): 32.04556374731508, (28, 974): 31.327525254087167, (28, 998): 31.47759011972483, (28, 1014): 31.309559433647195, (28, 1086): 46.45389126283928, (28, 1087): 47.984767570009076, (28, 1089): 47.64141797272009, (28, 1090): 47.32409605514665, (28, 1092): 46.66292742060661, (28, 1097): 46.87483773922499, (28, 1107): 47.28564691627544, (28, 1387): 165.58638591409579, (28, 1554): 176.6462110561251, (28, 1827): 30.213481363961534, (28, 1828): 30.370745285596897, (28, 1829): 30.435622512271138, (28, 1830): 29.972998015388836, (28, 1831): 30.10117219822263, (28, 1832): 30.04993655388623, (28, 1833): 30.117222446343263, (28, 1836): 30.095136250437932, (28, 1841): 30.503861007638694, (28, 1843): 30.295796365604886, (28, 1844): 30.332255932549565, (28, 1845): 30.034783017512613, (28, 1847): 29.41288806589462, (28, 1848): 29.66210260133552, (28, 1849): 30.804040357083384, (28, 1850): 30.98131440217099, (28, 1851): 29.699457460507546, (28, 1852): 29.590015829178107, (28, 1854): 29.81428990864025, (28, 1856): 29.19233914199151, (28, 1857): 29.569408673872704, (28, 1858): 30.772680884153715, (28, 1861): 30.30037461968597, (28, 1866): 29.059755705425317, (28, 1867): 30.629986551358954, (28, 1868): 30.576811982633654, (28, 1870): 30.146515498972658, (28, 1871): 30.707677309489064, (28, 1875): 29.889165245195922, (28, 1880): 29.475444721692618, (28, 1882): 29.358709761658822, (28, 1883): 31.135140810089528, (28, 1889): 29.847474973230387, (28, 1893): 30.685601282484363, (28, 1894): 30.543381568118864, (28, 1899): 29.78571983133389, (28, 1900): 29.97305183954523, (28, 1902): 31.008533695488044, (28, 1905): 31.157653950985843, (28, 1907): 29.98455226279627, (28, 1910): 30.25274822773882, (28, 1917): 32.13767086345539, (28, 1920): 30.130184428673648, (28, 1935): 31.467351662340135, (28, 1937): 31.62403503787002, (28, 1946): 29.740108772581298, (28, 1949): 30.049649688727243, (28, 1950): 28.84245707808649, (28, 1951): 29.335023048667857, (28, 1952): 29.232522184989914, (28, 1953): 29.721061783392177, (28, 1954): 29.268868533844483, (28, 1958): 29.80868464683193, (28, 1960): 30.09758270799617, (28, 1968): 30.21510592693057, (28, 1969): 31.80968701133016, (28, 1974): 31.36518701656564, (28, 1975): 31.262651347802326, (28, 1979): 30.89258232661342, (28, 1980): 30.542242538538066, (28, 1981): 30.899060284120655, (28, 1985): 31.121547654568246, (28, 1994): 27.843722617244836, (28, 2011): 29.26290564701049, (28, 2019): 31.07046427942154, (28, 2020): 30.8207454005875, (28, 2029): 29.686841391035117, (28, 2030): 30.652341929505784, (28, 2032): 29.4000499399698, (28, 2033): 30.101074101528006, (28, 2034): 29.993513793888134, (28, 2036): 28.517171984271013, (28, 2037): 28.90410132867691, (28, 2038): 29.449564014302254, (28, 2042): 32.63901465798875, (28, 2050): 30.110467093574556, (28, 2051): 29.95164113279802, (28, 2053): 30.08415755977037, (28, 2054): 30.358474155027206, (28, 2066): 29.781371394091032, (28, 2067): 29.842535410157154, (28, 2071): 27.42723323963617, (28, 2072): 28.03199043648869, (28, 2073): 27.144021170129843, (28, 2074): 26.96699971979751, (28, 2080): 25.890961719952234, (28, 2082): 28.324413345007603, (28, 2083): 28.646546495332167, (28, 2089): 28.210040056690094, (28, 2090): 28.537123390274694, (28, 2092): 28.303816882957065, (28, 2098): 26.424593120562577, (28, 2099): 26.59608574712931, (28, 2101): 26.21816428208656, (28, 2102): 27.73073068774613, (28, 2103): 27.193010158222975, (28, 2104): 26.829173857961134, (28, 2106): 28.765894332629657, (28, 2112): 26.276717140735876, (28, 2113): 27.857221743505452, (28, 2114): 27.98332167842492, (28, 2117): 28.887239226274314, (28, 2123): 34.73587862077166, (28, 2124): 34.993775701708294, (28, 2134): 33.581357042386585, (28, 2138): 34.61440705710913, (28, 2141): 33.878662770492205, (28, 2148): 31.7776736873542, (28, 2150): 33.127940736908386, (28, 2151): 33.204495296452684, (28, 2152): 32.80622295861174, (28, 2153): 32.095528581888225, (28, 2154): 31.122065284372063, (28, 2155): 30.581190766351472, (28, 2156): 30.66947378738119, (28, 2157): 29.494947770150702, (28, 2160): 33.771535127117914, (28, 2161): 32.50028707117695, (28, 2162): 31.265912075011276, (28, 2163): 30.94946682171569, (28, 2164): 30.7843560984331, (28, 2168): 31.90398014157793, (28, 2172): 31.02787026793305, (28, 2174): 32.84532786881692, (28, 2178): 30.935371710779247, (28, 2179): 30.66843923421083, (28, 2183): 34.29857724436194, (28, 2185): 34.15724976746944, (28, 2186): 34.031302617106405, (28, 2190): 34.09350124290714, (28, 2192): 33.80295404093035, (28, 2193): 34.46077030736674, (28, 2194): 34.175700002839086, (28, 2195): 33.791897979598126, (28, 2197): 33.70471397788746, (28, 2205): 32.82203215609161, (28, 2207): 31.77823139742155, (28, 2208): 32.29619017032047, (28, 2212): 35.29732499059028, (28, 2214): 23.54885329719847, (28, 2225): 23.251216587656387, (28, 2231): 30.545963722765237, (28, 2278): 24.87836530077215, (28, 2284): 25.318874425257484, (28, 2285): 25.055316732809597, (28, 2291): 22.4359858052973, (28, 2292): 23.806569924254145, (28, 2307): 24.747955316224893, (28, 2313): 21.907439175979793, (28, 2317): 23.7781917189717, (28, 2319): 23.959081141560635, (28, 2321): 24.1341978476537, (28, 2323): 24.430376093325417, (28, 2326): 26.514265280441634, (28, 2327): 26.166546939841634, (28, 2329): 25.892702880736376, (28, 2330): 25.49409109458072, (28, 2332): 25.900661021166357, (28, 2344): 25.554644861037215, (28, 2346): 25.270071051872147, (28, 2361): 27.620546294612037, (28, 2368): 30.093452254604536, (28, 2374): 30.303265382098527, (28, 2375): 30.55191619524939, (28, 2377): 29.383247454100136, (28, 2378): 30.70128299657583, (28, 2379): 30.50998194541439, (28, 2380): 30.80625830879859, (28, 2383): 29.89128128859693, (28, 2385): 30.18434872457284, (28, 2395): 30.43712269873094, (28, 2397): 30.244375453885112, (28, 2398): 28.99545949921103, (28, 2399): 29.581806417376548, (28, 2400): 29.482729270860357, (28, 2402): 29.551155992662025, (28, 2403): 29.839650554490508, (28, 2404): 30.007853204549633, (28, 2405): 29.23140997780485, (28, 2407): 30.001905580877132, (28, 2408): 30.241235916129664, (28, 2409): 29.502917104514513, (28, 2411): 29.46912139584241, (28, 2412): 29.527740682559124, (28, 2413): 29.71971790165456, (28, 2414): 29.27671984540516, (28, 2422): 29.254593512634802, (28, 2424): 29.691439702227036, (28, 2426): 29.830449943182238, (28, 2433): 29.137920422435975, (28, 2436): 28.748182796093616, (28, 2437): 27.135306854912923, (28, 2440): 27.554297091294178, (28, 2445): 34.49023932246973, (28, 2447): 33.46001863428757, (28, 2454): 34.51079555497388, (28, 2455): 34.645549120879025, (28, 2460): 31.29975917740538, (28, 2461): 31.691306082857988, (28, 2471): 38.0240189035531, (28, 2492): 32.69529401776882, (28, 2511): 28.249200907379535, (28, 2523): 30.52190214208544, (28, 2525): 30.282501803992403, (28, 2535): 29.328136639159073, (28, 2537): 28.566250308876107, (28, 2538): 29.061486808756015, (28, 2539): 29.038103376408266, (28, 2540): 29.678082749756943, (28, 2542): 30.291788511465704, (28, 2559): 41.138016916172035, (28, 2575): 40.22568250774188, (28, 2599): 24.143041971184445, (28, 2600): 27.472331825296088, (28, 2607): 25.85745495783833, (28, 2627): 33.188327247722775, (28, 2647): 35.85383130217322, (28, 2674): 33.791518509401314, (28, 2681): 34.002567880163646, (28, 2683): 34.760665611731895, (28, 2686): 33.39539473896594, (28, 2689): 47.062960192355064, (28, 2690): 47.23283449351993, (28, 2713): 53.37611969902238, (28, 2714): 54.14440940667774, (28, 2715): 54.43314074968582, (28, 2739): 54.01323652366447, (28, 2740): 50.668244460363645, (28, 2741): 50.71125947039114, (28, 2749): 54.20740477750773, (28, 2750): 54.09568394924622, (28, 2752): 54.21045318599891, (28, 2755): 54.56521877826731, (28, 2758): 54.66737499934684, (28, 2759): 54.577936708251066, (28, 2769): 54.01362499117659, (28, 2771): 51.52827078751508, (28, 2779): 53.04911925558291, (28, 2784): 50.479182005629085, (28, 2800): 52.64793134038231, (28, 2802): 50.840847597002245, (28, 2803): 50.55061068208965, (28, 2804): 50.282949132518176, (28, 2805): 51.63431981527299, (28, 2807): 51.431600338985774, (28, 2809): 51.73660290188358, (28, 2812): 49.38686438722609, (28, 2814): 52.91222864165408, (28, 2817): 54.7931191009509, (28, 2819): 51.02560782421215, (28, 2823): 51.250469606613756, (28, 2832): 52.26174908133547, (28, 2836): 50.91777461010321, (28, 2839): 51.241937689232806, (28, 2841): 53.922219229380694, (28, 2843): 53.502093367406644, (28, 2846): 51.95667446323422, (28, 2849): 52.787561905608435, (28, 2852): 52.36210576953247, (28, 2853): 52.99502543109458, (28, 2876): 54.02296318540774, (28, 2877): 55.22392117200902, (28, 2885): 57.43320690490486, (28, 2918): 50.068229917390035, (28, 2921): 50.7483798626929, (28, 2925): 47.0421854149523, (28, 2926): 45.540284281224075, (28, 2930): 49.85711134431364, (28, 2931): 47.69363106445465, (28, 2938): 50.36962913390322, (28, 2940): 50.44274259133349, (28, 2947): 48.43663228229158, (28, 2949): 49.162565398213296, (28, 2950): 49.67030835807947, (28, 2952): 49.44222067048811, (28, 2958): 49.274829700123064, (28, 2959): 49.16814146046646, (28, 2960): 49.809855557638016, (28, 2961): 49.68739257991834, (28, 2963): 49.24542108069631, (28, 2968): 49.57309817119297, (28, 2976): 49.00293572205873, (28, 2981): 46.96240018411853, (28, 2982): 47.26227257080605, (28, 2984): 47.14530138769631, (28, 3003): 47.24749432923101, (28, 3046): 39.74907165569563, (28, 3050): 44.13131524449152, (28, 3051): 44.15385909669217, (28, 3053): 43.83650125234837, (28, 3069): 47.20980097537513, (28, 3071): 42.8177080594508, (28, 3080): 58.14673781352592, (28, 3199): 49.34998973269982, (28, 3200): 49.21745059235139, (28, 3205): 51.78443873842578, (28, 3209): 49.507419944350445, (28, 3215): 48.98154288325995, (28, 3217): 48.49952901318864, (28, 3249): 48.75009544755269, (28, 3263): 52.47255940642533, (28, 3289): 49.21514968630131, (28, 3301): 49.991917152975965, (28, 3302): 49.56793727941324, (28, 3307): 49.27235155515593, (28, 3310): 50.20941655120071, (28, 3391): 64.63389094016138, (28, 3509): 79.13414158237751, (28, 3510): 79.6285359677731, (28, 3511): 79.21607132811872, (28, 3512): 79.45217371838578, (28, 3514): 79.28592977760961, (28, 3519): 78.43013798312907, (28, 3536): 78.11477175237351, (28, 3545): 77.25525918289784, (28, 3548): 77.91525008931235, (28, 3572): 77.93495167134685, (28, 3581): 78.82896483055785, (28, 3583): 78.80618349984387, (28, 3601): 77.67098682561391, (28, 3656): 78.87650825071216, (28, 3669): 80.82278788732275, (28, 3670): 80.44292672911058, (28, 3695): 82.45565451186873, (28, 3696): 82.09793973978695, (28, 3782): 76.83642404942836, (28, 3792): 77.476111114734, (28, 3989): 295.26187640934324, (28, 4008): 297.9012323439723, (28, 4031): 297.48734593455015, (28, 4045): 296.78191414980427, (28, 4144): 297.14701519951774, (28, 4145): 294.7269750701409, (28, 4164): 296.1823212342716, (28, 4168): 295.4669645887878, (28, 4173): 295.3523154452244, (28, 4181): 293.7391035033826, (28, 4228): 291.9701984984402, (28, 4248): 291.63586812937774, (28, 4254): 277.95928513313305, (28, 4260): 277.9358957672211, (28, 4262): 278.9262233054825, (28, 4273): 278.67173441618235, (28, 4319): 270.0903773796098, (28, 4326): 269.7818518746737, (28, 4328): 269.8841416742861, (28, 4334): 270.48425571074074, (28, 4335): 270.27866591717134, (28, 4372): 254.65896944933877, (28, 4413): 262.1913621987709, (28, 4434): 254.4667849921247, (28, 4447): 255.96080977460375, (28, 4452): 254.5097182847855, (28, 4463): 235.13322830158634, (28, 4465): 235.87612914898446, (28, 4619): 261.6748699127959, (28, 4645): 263.82346736722565, (28, 4657): 263.33196265817, (28, 4666): 262.4170172433285, (28, 4676): 263.76236180290516, (28, 4678): 264.15249513611985, (28, 4689): 263.00963104804714, (28, 4704): 269.65607539301936, (28, 4726): 281.42062885484364, (28, 4727): 281.18414801121116, (28, 4730): 280.74089009813275, (28, 4731): 280.7671786405473, (28, 4734): 281.60196121036137, (28, 4735): 281.29117908043264, (28, 4736): 281.3289675874215, (28, 4737): 280.8288487743616, (28, 4738): 280.8210546403731, (28, 4756): 281.0112896830008, (28, 4760): 280.24950072248674, (28, 4761): 280.5539764248874, (28, 4762): 279.8225244186475, (28, 4765): 280.3149178229302, (28, 4773): 281.97093386594554, (28, 4774): 281.6121634413658, (28, 4790): 281.83579117551307, (28, 4795): 281.6660426057869, (28, 4799): 281.6362790230327, (28, 4801): 281.92987749795503, (28, 4804): 281.9310237050052, (28, 4805): 281.78933773726965, (28, 4806): 281.3045353392327, (28, 4815): 280.94775196165216, (28, 4816): 281.6078566546676, (28, 4817): 281.55492612638284, (28, 4826): 281.2541470888566, (28, 4830): 280.8452607360023, (28, 4839): 280.93018278903645, (28, 4840): 281.0688612412183, (28, 4841): 280.51140683459005, (28, 4846): 280.3759986122015, (28, 4848): 280.17633194657077, (28, 4850): 280.36641874495723, (28, 4871): 278.2902709232374, (28, 4883): 280.1951620931536, (28, 4900): 279.4195537407042, (28, 4901): 279.0094547208672, (28, 4917): 258.72019606593716, (28, 4931): 256.8264783616299, (28, 4944): 259.0459098102118, (28, 4956): 257.0627772820086, (28, 4958): 256.7885073675373, (28, 4959): 256.27852834803707, (28, 4961): 257.5358366315789, (28, 4966): 256.4728108675425, (28, 5207): 254.35265952398487, (28, 5272): 225.6810013779642, (28, 5283): 226.28283612689566, (28, 5287): 226.7330479311375, (28, 5289): 226.97850000212097, (28, 5293): 226.29282459464002, (28, 5295): 228.05082360722224, (28, 5296): 227.72671792436293, (28, 5298): 227.5319910887568, (28, 5303): 227.78534197449392, (28, 5305): 224.71094746270418, (28, 5306): 223.7797010458999, (28, 5307): 224.3597945262998, (28, 5308): 224.89640751777418, (28, 5313): 225.26507951704082, (28, 5314): 225.77785402593526, (28, 5317): 224.69570423702973, (28, 5319): 227.10370603169878, (28, 5324): 226.9874685917231, (28, 5326): 226.93111879940724, (28, 5348): 223.3640007408704, (28, 5351): 223.38657001863672, (28, 5399): 226.87791326088737, (28, 5413): 223.49056073344178, (28, 5422): 227.52884187111027, (28, 5445): 225.94782050339387, (28, 5448): 225.34224495953504, (28, 5456): 224.86803015021638, (28, 5467): 225.34275304256224, (28, 5624): 219.7814781671934, (28, 5671): 243.6397085855876, (28, 5672): 242.84222157720086, (28, 5797): 253.42998627568522, (28, 5871): 232.55375362561338, (28, 5976): 225.1664065672171, (28, 6118): 56.378680218685304, (28, 6248): 67.21919396924608, (28, 6345): 195.12035778658904, (28, 6352): 192.93389055879868, (28, 6354): 195.60506169854497, (28, 6359): 196.12802477024806, (28, 6376): 193.51214165683686, (28, 6378): 195.35555311736576, (28, 6381): 196.0122781224637, (28, 6383): 194.61943561458116, (28, 6396): 196.1373766597525, (28, 6399): 195.25890619612923, (28, 6408): 192.91931570984866, (28, 6409): 193.71125742039467, (28, 6419): 189.79768841421026, (28, 6422): 193.01667922700648, (28, 6423): 192.82640347760994, (28, 6424): 195.12848233659798, (28, 6439): 194.63319901501768, (28, 6464): 193.95283783280468, (28, 6465): 193.8107270086895, (28, 6469): 194.25278177045055, (28, 6470): 194.15767262606715, (28, 6472): 196.90583367525448, (28, 6480): 196.0687034105664, (28, 6486): 197.01597014016798, (28, 6497): 196.67568666516243, (28, 6503): 193.6774110371049, (28, 6508): 194.05541890933478, (28, 6509): 194.38260834739643, (28, 6521): 196.18397241299525, (28, 6544): 195.81982557567542, (28, 6552): 192.99672420051166, (28, 6553): 192.62989442639682, (28, 6554): 192.25960981319403, (28, 6578): 193.64184910177607, (28, 6582): 193.14974889941382, (28, 6601): 193.76084894351905, (28, 6609): 196.8995891125247, (28, 6610): 196.95361157870684, (28, 6611): 197.15065775768826, (28, 6614): 197.04008157751943, (28, 6615): 197.06156869588963, (28, 6616): 197.27287326468317, (28, 6617): 197.16538440929455, (28, 6618): 197.5335598127432, (28, 6619): 196.75315306359806, (28, 6620): 197.2041776149985, (28, 6621): 196.8824952495772, (28, 6622): 197.00691909812207, (28, 6623): 196.9205094624295, (28, 6624): 196.56591210794434, (28, 6625): 196.55066442734574, (28, 6626): 196.77107687803618, (28, 6627): 197.03532339937323, (28, 6628): 197.06390501370674, (28, 6629): 196.556063132157, (28, 6630): 196.41500539939778, (28, 6632): 196.56739195972642, (28, 6634): 196.0332359418474, (28, 6635): 196.81358149531968, (28, 6636): 197.26348894595193, (28, 6637): 196.1270271283658, (28, 6638): 196.37635453548123, (28, 6639): 197.0198005156425, (28, 6640): 196.4680873160095, (28, 6641): 196.8155858809277, (28, 6642): 196.33086208223716, (28, 6643): 196.79395302711538, (28, 6645): 196.75975847249424, (28, 6646): 197.48305489362818, (28, 6647): 196.45223810705193, (28, 6653): 197.07225662590605, (28, 6655): 197.0494858772097, (28, 6658): 195.97938541880347, (28, 6662): 196.25724601217618, (28, 6819): 177.7206195868037, (28, 6996): 182.84176362018547, (28, 7059): 187.03336563350828, (28, 7187): 178.94579170973918, (28, 7304): 170.36550604374636, (28, 7528): 181.9455766323931, (28, 7720): 207.27201724618794, (28, 7793): 206.598255932262, (28, 7807): 206.98982234104193, (28, 7808): 206.44111353773374, (28, 7831): 198.63829742638512, (28, 7850): 202.9253265863267, (28, 7852): 202.1227040291437, (28, 8012): 206.36468446174518, (28, 8125): 209.00513279707724, (28, 8208): 214.94217077511945, (28, 8392): 200.78059603703733, (28, 8651): 157.69897250683124, (28, 9088): 177.93674359272367, (28, 9443): 145.6526799225768, (28, 9444): 146.24855706589372, (28, 9828): 127.23114082445092, (28, 9868): 126.50963302928514, (28, 10180): 209.3825437576201, (28, 10256): 220.1559371063851, (28, 10276): 215.24801496066198, (28, 10378): 216.87929856330447, (28, 10676): 205.59417331736302, (28, 10714): 198.48479496974656, (28, 10730): 199.8544983866113, (28, 10862): 194.42307297770577, (28, 10881): 196.1075328483217, (28, 10883): 195.8707844035018, (28, 10885): 194.07365465072698, (28, 10891): 195.50443819956612, (28, 10909): 195.47540702803892, (28, 10911): 195.83436946528371, (28, 10913): 195.40597167721393, (28, 10915): 195.45190044347487, (28, 10919): 195.7395878168583, (28, 11037): 182.96257488401514, (28, 11039): 179.21260354799696, (28, 11516): 320.61472560167215, (28, 11856): 270.7465936566356, (28, 11857): 270.3358431735672, (28, 11861): 270.5559586416849, (28, 11881): 270.1125015130929, (28, 11902): 268.2427013612487, (28, 11911): 267.9140727184866, (28, 11914): 268.1696691728524, (28, 11922): 269.55561280288725, (28, 11924): 269.99889361808926, (28, 11926): 269.46089584513334, (28, 11950): 270.5330262371779, (28, 11963): 272.29113675680856, (28, 11983): 271.09671875676224, (28, 11985): 273.172774535041, (28, 12009): 272.8271219816485, (28, 12010): 271.5807515145984, (28, 12018): 271.78577940037997, (28, 12020): 272.12501753131534, (28, 12021): 272.3312276438872, (28, 12024): 273.52365151429336, (28, 12025): 273.1213217059558, (28, 12027): 272.83881285354846, (28, 12031): 271.37207584583564, (28, 12032): 271.7875129003622, (28, 12035): 272.74638403598846, (28, 12041): 273.3221124019276, (28, 12045): 256.7421807874534, (28, 12145): 264.38076045178246, (28, 12275): 295.9624509978532, (28, 12294): 292.6798854303431, (28, 12358): 302.5117586037154, (28, 12463): 306.2745300188212, (28, 12465): 306.1559170975322, (28, 12482): 307.8983927033221, (28, 12503): 307.6497729003005, (28, 12506): 308.1091671531319, (28, 12549): 307.18001764988645, (28, 12559): 306.8168656022939, (28, 12569): 307.170370221458, (28, 12572): 307.5171008605996, (28, 12574): 306.799693602733, (28, 12576): 307.58685925560206, (28, 12591): 307.53980593714294, (28, 12608): 310.35464055768824, (28, 12696): 305.9072361246187, (28, 12710): 308.5634619530636, (28, 12728): 307.2430357091277, (28, 12766): 232.0611087800018, (28, 12771): 228.68824556706653, (28, 12790): 228.22924268543758, (28, 12795): 227.17010483266748, (28, 12797): 222.79830003176312, (28, 12798): 223.4026780951614, (28, 12811): 226.9037526353721, (28, 12830): 225.72223786599585, (28, 12848): 226.34992419915022, (28, 12850): 226.65618121285158, (28, 12852): 225.5605801984336, (28, 12854): 225.023246557467, (28, 12859): 226.88926756095395, (28, 12861): 224.00128686311186, (28, 12865): 227.55623081162526, (28, 12866): 227.2843845316777, (28, 12867): 228.3564616018589, (28, 12874): 227.83577898528753, (28, 12875): 228.24425058069806, (28, 12881): 226.57210085679054, (28, 12883): 227.2370942478633, (28, 12885): 228.59602124516206, (28, 12888): 226.93198683862968, (28, 12889): 226.78486759077268, (28, 12892): 227.94935940714646, (28, 12893): 226.95343124460038, (28, 12896): 227.27665942326536, (28, 12906): 227.8605066682528, (28, 13018): 223.07458568744093, (28, 13071): 223.15990545207143, (28, 13131): 218.77064292568548, (28, 13146): 222.29535323048472, (28, 13159): 217.56176594082513, (28, 13193): 218.0790231916895, (28, 13198): 211.8471261462061, (28, 13292): 218.97094885339962, (28, 13296): 220.99651415941756, (28, 13406): 208.0710208382978, (28, 13407): 207.8789238026532, (28, 13417): 207.51503719363677, (28, 13418): 208.20300375521822, (28, 13438): 210.83116425203573, (28, 13442): 211.33813472481475, (28, 13443): 210.82007669798227, (28, 13764): 168.20638675448762, (28, 13766): 168.8523738241088, (28, 13771): 168.43562745871296, (28, 13783): 167.3201577271186, (28, 13784): 169.467256514558, (28, 13792): 167.52722502935285, (28, 13824): 166.91667618395772, (28, 14017): 169.66622856353112, (28, 14870): 197.02485124407295, (28, 14997): 175.8094385832004, (28, 15000): 175.9335817582311, (28, 15003): 176.44809362303863, (28, 15006): 177.21782457318193, (28, 15007): 177.68195665697638, (28, 15056): 177.78786207815807, (28, 15063): 177.4124685532283, (28, 15069): 177.32891405790093, (28, 15076): 177.79163246081112, (28, 15086): 176.28526368969915, (28, 15087): 175.8614827959698, (28, 15111): 174.43291322241205, (28, 15116): 175.25792230902476, (28, 15722): 163.07198976270772, (28, 15998): 156.67593990863512, (28, 16073): 96.78308979182923, (28, 16939): 12.5, (28, 16940): 12.5, (28, 16951): 12.5, (28, 16963): 12.5, (28, 16965): 12.5, (28, 16969): 12.5, (28, 16970): 12.5, (28, 16971): 12.5, (28, 16973): 12.5, (28, 16974): 12.5, (28, 16976): 12.5, (28, 16978): 12.5, (28, 16980): 12.5, (28, 16982): 12.5, (28, 17045): 44.372450515973966, (28, 17048): 44.9398137190213, (28, 17304): 288.0520019080171, (28, 17305): 287.4938989596257, (28, 17330): 287.9629982890998, (28, 17334): 287.17006338497845, (28, 17343): 288.6174346932425, (28, 17345): 287.0359419180406, (28, 17347): 287.8339149353848, (28, 17351): 285.94912775009954, (28, 17372): 287.0317937306758, (28, 17373): 288.58017342511545, (28, 17377): 288.68052357943213, (28, 17382): 287.6508803000663, (28, 17383): 287.87632315061205, (28, 17389): 287.2603072605654, (28, 17400): 288.3252544229511, (28, 17401): 288.3207397794225, (28, 17402): 288.3764019906874, (28, 17403): 288.47085502995236, (28, 17440): 286.98685149224497, (28, 17455): 288.36935717587386, (28, 17491): 288.3905313703116, (28, 17507): 286.77646092033035, (28, 17509): 287.3780478037516, (28, 17590): 285.4495571289612, (28, 17615): 282.8614317357228, (28, 17642): 283.3953277309328, (28, 17643): 283.30943010496014, (28, 17668): 282.8599636782801, (28, 17721): 281.68810035398946, (28, 17754): 287.2041118820886, (28, 17769): 287.0760324891692, (28, 17776): 284.5987266676634, (28, 17804): 288.03294797786737, (28, 17809): 288.6144110650813, (28, 17824): 288.2944307003193, (28, 17837): 286.32457362991, (28, 17838): 286.33131081698804, (28, 17862): 285.871994220724, (28, 17866): 287.1356176639125, (28, 17872): 285.4894393300523, (28, 17873): 284.51129789258783, (28, 17881): 286.0036083272604, (28, 17947): 62.20952351685084, (28, 17951): 62.93775069235873, (28, 17953): 63.30717438853843, (28, 17954): 63.406184223215654, (28, 17959): 61.95827937936083, (28, 17963): 61.82924383844508, (28, 18000): 66.53414754252682, (28, 18001): 66.6161733470615, (28, 18111): 70.5689505219859, (28, 18148): 88.22478684458973, (28, 18166): 81.83885316883197, (28, 18189): 73.74024765278422, (28, 18239): 288.91396309040266, (28, 18240): 288.8922052391216, (28, 18245): 288.96063347112874, (28, 18247): 288.8176066412707, (28, 18251): 288.94036363814985, (28, 18256): 289.0560669291855, (28, 18258): 288.9015662339701, (28, 18259): 288.9197920111498, (28, 18260): 288.9651554116875, (28, 18262): 289.06241778057665, (28, 18263): 289.08583055937777, (28, 18264): 289.13191548541494, (28, 18266): 289.09229131701744, (28, 18267): 289.13946432181103, (28, 18268): 289.1570292463024, (28, 18269): 289.24940353129347, (28, 18275): 289.20575761160063, (28, 18285): 289.1221435809126, (28, 18308): 288.1460929995681, (28, 18313): 287.77334192693144, (28, 18314): 287.89778534880753, (28, 18315): 289.286339946445, (28, 18316): 289.2580090491797, (28, 18317): 289.29995093100973, (28, 18320): 289.3686990857445, (28, 18321): 289.3826456430631, (28, 18322): 289.4528421404573, (28, 18324): 289.5388790032105, (28, 18325): 289.7853099612016, (28, 18326): 289.69442696698883, (28, 18327): 289.3214100799358, (28, 18329): 289.918519901021, (28, 18330): 289.73244176428636, (28, 18331): 289.57748934940673, (28, 18332): 289.40742322512546, (28, 18333): 289.72476521527943, (28, 18336): 289.61667024480363, (28, 18337): 289.7132504267676, (28, 18403): 289.4746035634891, (28, 18432): 285.50742145923914, (28, 18451): 288.19639002778916, (28, 18466): 290.8534261032125, (28, 18481): 289.4033101332276, (28, 18483): 289.389312671141, (28, 18484): 289.2643327653527, (28, 18485): 288.90173017567037, (28, 18486): 289.3138469012004, (28, 18487): 289.01447603812835, (28, 18489): 289.23014454091395, (28, 18490): 289.5818296864558, (28, 18491): 289.7304182033802, (28, 18492): 288.685738085689, (28, 18493): 289.2769929303867, (28, 18494): 289.1587696541575, (28, 18495): 289.47312229864843, (28, 18496): 289.30633207068325, (28, 18497): 288.9578109218652, (28, 18498): 288.9759531632513, (28, 18499): 289.2023304214976, (28, 18501): 289.0621454254565, (28, 18502): 288.9187973061742, (28, 18503): 288.79257187580913, (28, 18504): 289.3512212117477, (28, 18506): 289.12195483383005, (28, 18507): 288.992694939287, (28, 18508): 289.1838077363594, (28, 18509): 289.1993766648023, (28, 18510): 288.8148686357185, (28, 18511): 289.3477455480708, (28, 18512): 289.1513732298625, (28, 18515): 289.384017792885, (28, 18516): 289.43919158986967, (28, 18517): 289.27696179445985, (28, 18518): 289.54727756370244, (28, 18519): 289.37480508459896, (28, 18520): 289.12496197490816, (28, 18522): 289.96514283924864, (28, 18523): 290.01163524769663, (28, 18532): 290.23533054027513, (28, 18535): 289.7856119654092, (28, 18537): 289.5352112335321, (28, 18539): 289.5951815526708, (28, 18540): 289.6323565372006, (28, 18541): 289.7622254795321, (28, 18542): 289.8432932971156, (28, 18543): 289.4464669308357, (28, 18546): 289.65948279581306, (28, 18555): 290.05326466993955, (28, 18556): 290.13464853553114, (28, 18565): 290.22560811916713, (28, 18567): 290.368683315096, (28, 18568): 290.1420141629511, (28, 18577): 291.6759801418037, (28, 18583): 291.37958678159714, (28, 18605): 291.65498304857954, (28, 18608): 290.5569933709964, (28, 18616): 293.0901248090856, (28, 18618): 294.33557125267146, (28, 18625): 293.81529560405494, (28, 18645): 292.6931658003817, (28, 18646): 293.00916263814287, (28, 18653): 292.089044248195, (28, 18654): 293.07570003440236, (28, 18655): 292.44827661698764, (28, 18666): 296.24296999276027, (28, 18837): 290.21272085169574, (28, 18974): 287.8284697455605, (28, 18999): 288.6706233685824, (28, 19000): 289.0366544009742, (28, 19174): 270.761123970175, (28, 19342): 277.9477429994267, (28, 19455): 274.0951185480225, (28, 19555): 255.80190609589832, (28, 19564): 256.75570922133, (28, 19573): 256.0018977080021, (28, 19586): 255.67361872668704, (28, 19605): 255.98591642452928, (28, 19611): 256.50018645720843, (28, 19614): 256.3005226732675, (28, 19641): 265.049995214786, (28, 19702): 264.85665615594957, (28, 19713): 264.22477145494133, (28, 19731): 252.99362375827218, (28, 19819): 271.2315719211986, (28, 19893): 251.03761818062196, (28, 19899): 254.76569971131116, (28, 19929): 252.10542084313303, (28, 19951): 259.84960175086115, (28, 19962): 252.56849675163008, (28, 19970): 254.6157552924266, (28, 19971): 254.5719097500793, (28, 19972): 253.86039172293457, (28, 19975): 253.60871421564195, (28, 19978): 261.8703386071014, (28, 19987): 262.06134752993916, (28, 19989): 259.91935194087597, (28, 20039): 262.48340967145987, (28, 20043): 263.4589454097205, (28, 20047): 262.8437145789128, (28, 20052): 260.4080380042849, (28, 20054): 260.55713669942526, (28, 20085): 271.8639564948467, (28, 20104): 272.55622918261565, (28, 20132): 268.2363358311064, (28, 20203): 249.84817820680738, (28, 20280): 248.7084164985237, (28, 20285): 248.37509250466263, (28, 20290): 249.13622389388814, (28, 20297): 248.4254171122244, (28, 20309): 261.8071415003396, (28, 20453): 273.6354669770205, (28, 20485): 243.928127340692, (28, 20520): 242.13914122660486, (28, 20526): 241.17147194603987, (28, 20698): 155.07893144346377, (28, 20868): 135.12576006855954, (28, 21042): 226.9644657953859, (28, 21057): 231.75798001192737, (28, 21066): 229.39858007380823, (28, 21075): 228.51162882522084, (28, 21093): 227.31222391492344, (28, 21098): 230.69712177228496, (28, 21127): 227.35188559076767, (28, 21130): 228.2499363477393, (28, 21144): 228.12640145281833, (28, 21146): 227.03872905652165, (28, 21147): 228.05020060180613, (28, 21148): 228.87755303620133, (28, 21153): 226.95141954978953, (28, 21293): 234.88552386597073, (28, 21426): 233.80829843236364, (28, 21442): 238.92688107463613, (28, 21451): 239.41962718919916, (28, 21466): 236.34651461613785, (28, 21469): 237.09804597103474, (28, 21471): 235.96567981443047, (28, 21473): 236.58529329168752, (28, 21475): 236.0292109934841, (28, 21482): 237.57792644735576, (28, 21484): 237.41873961968543, (28, 21488): 236.97953231072748, (28, 21494): 236.01728493648633, (28, 21498): 236.57928980778928, (28, 21500): 235.68412649598983, (28, 21514): 237.17430732197488, (28, 21537): 235.5075355590824, (28, 21662): 237.83206926122196, (28, 21691): 234.87432581345894, (28, 21757): 229.66242210968036, (28, 21777): 217.6739593263286, (28, 21778): 216.9281670992763, (28, 21779): 217.3357817763896, (28, 21790): 218.52359999517708, (28, 21802): 218.46630902428785, (28, 21824): 219.23260748678112, (28, 21874): 217.5185067264377, (28, 21879): 217.06345875301093, (28, 21983): 220.30301457770722, (28, 22002): 228.27683140474088, (28, 22132): 223.46137315165166, (28, 22261): 126.317086928288, (28, 22298): 128.3164442150252, (28, 22339): 122.38314713028673, (28, 22508): 139.60692296580012, (28, 22841): 98.70590996827833, (28, 22842): 98.37587618605669, (28, 22874): 96.34392632990986, (28, 22941): 97.56880023821783, (28, 22956): 97.82391272848135, (28, 22960): 98.78242115446818, (28, 22968): 94.80563126760687, (28, 22970): 95.61108186586726, (28, 22974): 93.06209956257378, (28, 22980): 93.7340431812639, (28, 23025): 89.62824072123819, (28, 23028): 88.64166801676281, (28, 23081): 84.91433007949662, (28, 23104): 76.86166136593843, (28, 23147): 82.59112191326587, (28, 23298): 250.09784314602848, (28, 23376): 247.95854570666287, (28, 23381): 246.67015591195727, (28, 23529): 251.45695826360165, (28, 23556): 250.22090429713913, (28, 23718): 248.79057040870933, (28, 24001): 262.7554913437113, (28, 24094): 266.72428774005044, (28, 24129): 268.84504077500355, (28, 24174): 264.45305391093535, (28, 24235): 269.17409669696605, (28, 24259): 271.18895316333885, (28, 24260): 271.03880211264385, (28, 24261): 270.58246416290405, (28, 24305): 273.6021790399341, (28, 24306): 274.014268768858, (28, 24307): 273.3954888154731, (28, 24308): 268.0013890308209, (28, 24498): 278.89577602671693, (28, 24499): 278.9436010400565, (28, 24500): 278.5506113133445, (28, 24668): 275.8064231987834, (28, 24711): 281.58897875161705, (28, 24756): 283.0697946163668, (28, 24788): 283.64844872957866, (28, 24809): 281.36492005098745, (28, 24813): 282.0704579705208, (28, 24821): 281.8351136424526, (28, 24825): 282.02510890268087, (28, 24832): 281.1977229726687, (28, 24833): 281.55517795518404, (28, 24835): 281.9160240538722, (28, 24837): 282.4733274061036, (28, 24840): 281.1482617917449, (28, 24841): 281.688357917996, (28, 24844): 281.17253659578137, (28, 24845): 281.46680677516923, (28, 24846): 281.4799713253115, (28, 24849): 281.6786442827294, (28, 24850): 282.18944367477224, (28, 24863): 277.1594546005629, (28, 24866): 277.79547891593523, (28, 24885): 278.57999469294674, (28, 24886): 278.65301301743744, (28, 24889): 279.98787611491366, (28, 24903): 280.49983871807405, (28, 24909): 278.1265873174354, (28, 24999): 305.3625660667732, (28, 25019): 304.5307472101893, (28, 25028): 305.011979648781, (28, 25137): 249.22539489345155, (28, 25145): 250.0621175921014, (28, 25208): 258.86310741785064, (28, 25233): 257.7051077254891, (28, 25371): 249.8135330635031, (28, 25377): 247.5983478506982, (28, 25828): 205.4908721679226, (28, 25851): 199.34333200438655, (28, 25874): 205.34152629331442, (28, 25898): 207.8547572713555, (28, 25946): 204.8513281934151, (28, 26047): 217.81749293236018, (28, 26066): 233.9846135522641, (28, 26197): 223.72367374299117, (28, 26212): 184.40055929495148, (28, 26253): 182.312950414581, (28, 26254): 183.081995950971, (28, 26257): 183.89631253044809, (28, 26258): 182.7568563012438, (28, 26260): 183.33633172279266, (28, 26266): 182.347092767318, (28, 26267): 183.06365443105992, (28, 26271): 183.11072196601333, (28, 26304): 190.4391985042884, (28, 26305): 190.3224605411334, (28, 26363): 203.16595618163973, (28, 26441): 137.35710918265747, (28, 26442): 137.27261706543246, (28, 26450): 138.2108538594313, (28, 26459): 139.3847093436548, (28, 26462): 139.74708894280272, (28, 26467): 137.2461972526876, (28, 26471): 137.37178800283917, (28, 26472): 137.27979396335004, (28, 26473): 137.14808270519617, (28, 26476): 135.9175319439518, (28, 26485): 138.40206121009783, (28, 26493): 137.80737460585408, (28, 26524): 139.86931524878636, (28, 26525): 139.66104035134484, (28, 26556): 137.76571005372142, (28, 26560): 138.79046215406913, (28, 26561): 139.5481597156245, (28, 26564): 137.74247766339434, (28, 26569): 139.36914698825157, (28, 26570): 139.22783196775342, (28, 26573): 138.59064245031584, (28, 26581): 138.16864371419882, (28, 26583): 138.63174027096707, (28, 26593): 137.60571969978835, (28, 26837): 136.6169216204366, (28, 26844): 136.262141994125, (28, 26863): 135.94991923408796, (28, 26893): 134.44576697128105, (28, 26902): 133.91917242521413, (28, 26905): 135.44364079025948, (28, 26912): 134.72153158657264, (28, 26921): 135.29435293704958, (28, 26922): 134.86744339568585, (28, 27212): 158.73766140230705, (28, 27218): 160.20651422080758, (28, 27239): 157.94941798686241, (28, 27257): 157.83715855355828, (28, 27274): 157.61351778491576, (28, 27279): 157.2341432762371, (28, 27282): 157.5850829568709, (28, 27283): 158.29533290570762, (28, 27285): 157.19413503395933, (28, 27286): 156.7490964659878, (28, 27290): 157.8169343688225, (28, 27295): 158.6838461567562, (28, 27300): 157.7273890950997, (28, 27344): 156.71020905506012, (28, 27366): 155.87509523190786, (28, 27383): 156.24336366179116, (28, 27398): 156.89809358522436, (28, 27406): 157.5581326164411, (28, 27407): 157.81103600634873, (28, 27426): 161.23804741456823, (28, 27432): 161.79184991700967, (28, 27460): 161.83509712278007, (28, 27523): 149.03989980593565, (28, 27545): 150.95385721865892, (28, 27602): 141.79526612575796, (28, 27606): 142.3136700660157, (28, 27646): 140.33366228314097, (28, 27667): 138.39454520184157, (28, 27672): 138.6461285411604, (28, 27674): 138.75206925769302, (28, 27688): 139.86603870781215, (28, 27692): 137.91691975315027, (28, 27693): 138.1268392286905, (28, 27705): 137.74270097656472, (28, 27712): 137.30124061202721, (28, 27786): 156.8515183799771, (28, 27790): 162.5523336258235, (28, 27791): 163.34472800530662, (28, 27795): 156.64020768668223, (28, 27801): 160.41425652248415, (28, 27813): 156.11852103414552, (28, 27816): 157.321675137468, (28, 27823): 160.60368614516844, (28, 27830): 158.7153167773419, (28, 27884): 139.89808067917056, (28, 27885): 140.5652394706239, (28, 27896): 140.32397442225908, (28, 27919): 140.67241417465493, (28, 27922): 140.21066628785044, (28, 27930): 140.44408022635844, (28, 27934): 140.14176513579315, (28, 27935): 139.78702766230282, (28, 27948): 123.17272007608047, (28, 27951): 129.03173035919437, (28, 28061): 96.68957855837648, (28, 28290): 76.5627103868791, (28, 28292): 74.58444633712698, (28, 28293): 76.04310887338198, (28, 28295): 75.10626130474373, (28, 28296): 76.0066936871027, (28, 28297): 77.49518451548535, (28, 28302): 76.63897453020353, (28, 28310): 47.80888150208717, (28, 28313): 49.32489092179852, (28, 28372): 45.57892693015625, (28, 28398): 45.80315971768755, (28, 28399): 46.216876644880536, (28, 28400): 46.01862178996466, (28, 28401): 46.102918142432834, (28, 28445): 50.70695548710212, (28, 28475): 44.16252098482697, (28, 28885): 268.6525682659916, (28, 28886): 268.220408095179, (28, 28915): 268.44666011898187, (28, 28916): 268.1451834625123, (28, 28917): 267.9007294731632, (28, 28921): 269.4272787783107, (28, 28931): 269.28654630564205, (28, 28945): 266.88068841433704, (28, 28982): 267.5063969193203, (28, 29219): 269.10843803176397, (28, 29228): 267.3400647518883, (28, 29246): 278.451670768765, (28, 29248): 278.1534384156174, (28, 29282): 275.817264700586, (28, 29290): 279.75377615744566, (28, 29291): 279.24130843160276, (28, 29292): 279.7016838336339, (28, 29293): 278.78105957995854, (28, 29294): 279.4555212937616, (28, 29298): 278.81473151593065, (28, 29299): 278.69925189350187, (28, 29304): 277.9199045723916, (28, 29317): 275.75761851592927, (28, 29323): 275.59376167401734, (28, 29330): 276.62934870935203, (28, 29331): 277.17393203768006, (28, 29344): 269.03708430909353, (28, 29445): 248.16025627172667, (28, 29724): 110.67983216674429, (28, 29738): 110.8058553764557, (28, 29745): 110.9492677141182, (28, 29748): 113.59981415009781, (28, 29750): 114.88803820267808, (28, 29759): 113.11461950344943, (28, 29772): 113.61474916947394, (28, 29781): 113.57859966656578, (28, 29784): 112.38685851854194, (28, 29790): 114.1419410282615, (28, 29811): 114.99988651189206, (28, 29817): 122.63465457773346, (28, 29818): 122.64254772867451, (28, 29929): 109.29745245673338, (28, 30039): 103.91241533055754, (28, 30066): 98.64891502577963, (28, 30116): 100.19250234402323, (28, 30238): 104.40759439371796, (28, 30248): 94.48138060183689, (28, 30260): 93.7726659644834, (28, 30545): 262.8366591543888, (28, 30733): 243.7324579640512, (28, 30756): 238.32581519155121, (28, 30921): 247.7505842239353, (28, 31079): 198.92578528515557, (28, 31149): 196.56373237875877, (28, 31154): 196.5758051991965, (28, 31160): 196.42042775347701, (28, 31163): 196.27233751142455, (28, 31189): 188.37037594615794, (28, 31215): 188.79500244794338, (28, 31259): 187.617408463881, (28, 31262): 186.7733881744956, (28, 31430): 199.63849958215772, (28, 31568): 176.9647569897179, (28, 31751): 194.5137072605407, (29, 109): 41.008900633944705, (29, 872): 195.00724902495574, (29, 873): 195.92220041928604, (29, 877): 195.61155247548237, (29, 879): 195.75048005365696, (29, 884): 194.90474280338336, (29, 889): 195.46259688604786, (29, 891): 194.59302911212794, (29, 892): 196.45304302613349, (29, 894): 196.32413085521432, (29, 896): 195.3887241184148, (29, 903): 195.68340432742417, (29, 909): 194.01882061831571, (29, 910): 194.35547206360948, (29, 912): 193.7574111766785, (29, 913): 193.10932020226798, (29, 916): 192.79187989564792, (29, 926): 194.61678613602976, (29, 927): 194.30312746535793, (29, 948): 194.25597613755897, (29, 961): 194.65317058859824, (29, 962): 194.73626786453406, (29, 963): 194.83640951469732, (29, 967): 196.0569431171365, (29, 974): 195.64321316025973, (29, 998): 196.4462036691791, (29, 1014): 216.04432298295168, (29, 1086): 191.95023697375024, (29, 1087): 191.74269917510833, (29, 1089): 190.94899301096257, (29, 1090): 191.3412583990469, (29, 1092): 192.65685325833098, (29, 1097): 191.671743392673, (29, 1107): 193.25316342476052, (29, 1387): 55.41334263604446, (29, 1554): 41.38762371608114, (29, 1827): 237.5145718572485, (29, 1828): 237.59664184165914, (29, 1829): 237.74767136631286, (29, 1830): 237.67450212721198, (29, 1831): 237.7438633829829, (29, 1832): 237.6381855374505, (29, 1833): 237.63688300747464, (29, 1836): 237.5172682231995, (29, 1841): 238.12299824003424, (29, 1843): 237.87682257280645, (29, 1844): 237.99870861580806, (29, 1845): 237.71640929601668, (29, 1847): 236.73131224880052, (29, 1848): 237.06247608050802, (29, 1849): 238.62685089758335, (29, 1850): 238.77795274237613, (29, 1851): 237.34885500673454, (29, 1852): 237.40170107013432, (29, 1854): 237.53762320204498, (29, 1856): 236.72204098537992, (29, 1857): 237.05545211950658, (29, 1858): 238.4561299290324, (29, 1861): 237.75131696181595, (29, 1866): 236.72571346510318, (29, 1867): 238.11589242402337, (29, 1868): 237.89497987621448, (29, 1870): 238.00853235923088, (29, 1871): 238.04727009234517, (29, 1875): 237.5015019981973, (29, 1880): 236.90342314002282, (29, 1882): 237.04192731885786, (29, 1883): 238.75820796209217, (29, 1889): 237.028082320878, (29, 1893): 237.7191619043908, (29, 1894): 237.47918310656766, (29, 1899): 236.8040910201393, (29, 1900): 236.96528217883684, (29, 1902): 238.12149557117752, (29, 1905): 238.43917818434628, (29, 1907): 237.256886660622, (29, 1910): 237.33201254074513, (29, 1917): 238.97611749958074, (29, 1920): 237.25420609622833, (29, 1935): 238.42546665209105, (29, 1937): 238.6895881359823, (29, 1946): 236.22468134005268, (29, 1949): 236.49434719158467, (29, 1950): 235.5684617941139, (29, 1951): 236.0309436809611, (29, 1952): 236.46566334350666, (29, 1953): 236.55336286407984, (29, 1954): 236.37695921225014, (29, 1958): 236.44442739113873, (29, 1960): 236.9453006288543, (29, 1968): 237.14280045308297, (29, 1969): 238.4286546080608, (29, 1974): 238.09734723429892, (29, 1975): 238.11233397785236, (29, 1979): 237.39270357714193, (29, 1980): 237.39562497238686, (29, 1981): 237.55946311434246, (29, 1985): 237.70804288284154, (29, 1994): 235.31310360255554, (29, 2011): 237.04947422906864, (29, 2019): 239.51857772230272, (29, 2020): 239.19246525964843, (29, 2029): 238.0112330615286, (29, 2030): 238.96551879645455, (29, 2032): 237.84765516141584, (29, 2033): 238.446233189676, (29, 2034): 238.4641596009318, (29, 2036): 237.39392156351687, (29, 2037): 237.66303187380055, (29, 2038): 237.62980595181958, (29, 2042): 241.2973384094674, (29, 2050): 238.2392186552343, (29, 2051): 238.21731626448567, (29, 2053): 238.3010292357988, (29, 2054): 238.62657408938867, (29, 2066): 237.9695476811013, (29, 2067): 237.9557826054491, (29, 2071): 234.68626779890866, (29, 2072): 235.2694784975285, (29, 2073): 233.52723473098433, (29, 2074): 233.46470982273013, (29, 2080): 232.49105406815968, (29, 2082): 235.59093328119226, (29, 2083): 235.89064392664633, (29, 2089): 235.20493312121658, (29, 2090): 235.47926961454317, (29, 2092): 235.06413888612548, (29, 2098): 232.84225762182896, (29, 2099): 233.21285578099173, (29, 2101): 232.80617301651003, (29, 2102): 234.41884625683898, (29, 2103): 233.9230374075294, (29, 2104): 233.6650174671375, (29, 2106): 236.11389161865327, (29, 2112): 233.04648657713244, (29, 2113): 234.6654837687982, (29, 2114): 235.10242402723387, (29, 2117): 236.38079866914654, (29, 2123): 232.94255791496573, (29, 2124): 233.2752744424826, (29, 2134): 232.39758604069831, (29, 2138): 233.34832253395155, (29, 2141): 232.49117637287299, (29, 2148): 233.25481955656682, (29, 2150): 231.69450197271337, (29, 2151): 232.06480187184692, (29, 2152): 231.52923035550336, (29, 2153): 233.34041121437747, (29, 2154): 231.94449749817858, (29, 2155): 231.83323634380739, (29, 2156): 231.54280077162448, (29, 2157): 232.06682790142455, (29, 2160): 233.94588954731833, (29, 2161): 231.49914586785079, (29, 2162): 233.5050549832167, (29, 2163): 233.02822318994455, (29, 2164): 233.01412964447354, (29, 2168): 231.97073866050522, (29, 2172): 232.40982040389477, (29, 2174): 232.0591985568251, (29, 2178): 232.72076211446583, (29, 2179): 232.51628842955256, (29, 2183): 233.3572770831889, (29, 2185): 233.39522369381547, (29, 2186): 233.1206224250981, (29, 2190): 233.9808502535927, (29, 2192): 233.49224135042073, (29, 2193): 233.441068751044, (29, 2194): 232.94214541594985, (29, 2195): 232.90642160605717, (29, 2197): 233.61718865942603, (29, 2205): 232.97098896034655, (29, 2207): 232.11869551013507, (29, 2208): 232.60274380363438, (29, 2212): 233.50732724998682, (29, 2214): 224.1009390759076, (29, 2225): 225.3952220161057, (29, 2231): 222.27484961774886, (29, 2278): 230.57184185526683, (29, 2284): 231.65467756044103, (29, 2285): 231.5376807088367, (29, 2291): 229.68368298157662, (29, 2292): 229.69837374601013, (29, 2307): 230.99660333292724, (29, 2313): 229.5090752398418, (29, 2317): 228.86238860210062, (29, 2319): 230.06960504724336, (29, 2321): 230.57202020266436, (29, 2323): 230.45281020376757, (29, 2326): 232.13198120112986, (29, 2327): 231.6897688880977, (29, 2329): 231.39377696662686, (29, 2330): 231.06995792086227, (29, 2332): 231.8251315207959, (29, 2344): 230.6159723972182, (29, 2346): 230.63478258533257, (29, 2361): 230.13801959375508, (29, 2368): 235.48187589024198, (29, 2374): 235.9989014058992, (29, 2375): 236.14228887342327, (29, 2377): 234.41278406638273, (29, 2378): 236.4658946980168, (29, 2379): 236.54810962303543, (29, 2380): 236.68830070630838, (29, 2383): 234.84302656382187, (29, 2385): 235.09221923830756, (29, 2395): 235.08698777712164, (29, 2397): 236.3634729953225, (29, 2398): 233.86612461622585, (29, 2399): 234.461129576628, (29, 2400): 234.322847615193, (29, 2402): 235.40537676742383, (29, 2403): 235.78911913172763, (29, 2404): 235.8719564111089, (29, 2405): 234.96156955696912, (29, 2407): 235.68002976260294, (29, 2408): 236.1469071053618, (29, 2409): 235.23161892407393, (29, 2411): 235.85141650268332, (29, 2412): 235.7262746230665, (29, 2413): 236.0500454205564, (29, 2414): 235.54706158303642, (29, 2422): 235.75733032464638, (29, 2424): 235.82032739844797, (29, 2426): 235.89024432136537, (29, 2433): 235.20092413813452, (29, 2436): 235.0534175750991, (29, 2437): 232.80325080460509, (29, 2440): 233.28756520605708, (29, 2445): 243.53889526083495, (29, 2447): 242.28469836716593, (29, 2454): 243.42889163496912, (29, 2455): 243.46125924935023, (29, 2460): 239.9498779427161, (29, 2461): 240.39011362643598, (29, 2471): 247.6500131933978, (29, 2492): 241.40146128403515, (29, 2511): 237.6369233933363, (29, 2523): 239.56650612055822, (29, 2525): 239.10156025964602, (29, 2535): 239.35863260109963, (29, 2537): 238.59556620714898, (29, 2538): 239.09148927492257, (29, 2539): 239.01456480357515, (29, 2540): 239.70866236092627, (29, 2542): 240.31399898191083, (29, 2559): 251.0802909786713, (29, 2575): 250.25522021075855, (29, 2599): 233.078712250629, (29, 2600): 236.92901192433692, (29, 2607): 234.59428656759943, (29, 2627): 240.38214124553343, (29, 2647): 242.56288331280936, (29, 2674): 241.3242696275535, (29, 2681): 241.1208341036254, (29, 2683): 242.0932575099702, (29, 2686): 240.89204266290307, (29, 2689): 254.4498662615974, (29, 2690): 254.53595985256845, (29, 2713): 257.77870370834063, (29, 2714): 258.0950444157457, (29, 2715): 258.42231723646546, (29, 2739): 258.1055738806535, (29, 2740): 255.7922852189502, (29, 2741): 255.93774894920872, (29, 2749): 257.7482472762571, (29, 2750): 257.8186280031473, (29, 2752): 258.03760061164786, (29, 2755): 258.3168098868233, (29, 2758): 258.2681547041681, (29, 2759): 258.2548725213311, (29, 2769): 257.8378158244658, (29, 2771): 256.38557084921564, (29, 2779): 256.7196188955965, (29, 2784): 253.12587120612335, (29, 2800): 254.02156046560816, (29, 2802): 255.2799621405192, (29, 2803): 255.1260171833743, (29, 2804): 254.8950639712535, (29, 2805): 255.64463533706052, (29, 2807): 255.59454143526202, (29, 2809): 255.53838719217174, (29, 2812): 253.35465838709518, (29, 2814): 255.6251575454781, (29, 2817): 255.96865030325148, (29, 2819): 255.565221368616, (29, 2823): 253.81724016740333, (29, 2832): 256.09489698772796, (29, 2836): 254.61050247095415, (29, 2839): 255.5598555518719, (29, 2841): 255.9038647154965, (29, 2843): 255.7452871257196, (29, 2846): 255.0236233815209, (29, 2849): 256.3765865934934, (29, 2852): 256.02049375826783, (29, 2853): 256.54232884142294, (29, 2876): 256.83156897810017, (29, 2877): 258.04278606849994, (29, 2885): 258.68977370221944, (29, 2918): 255.5460294300531, (29, 2921): 256.09368798334816, (29, 2925): 253.42949269963034, (29, 2926): 252.48681973100562, (29, 2930): 254.76643982734558, (29, 2931): 253.73143763876075, (29, 2938): 255.60355494304844, (29, 2940): 256.85461743366153, (29, 2947): 255.03836104356287, (29, 2949): 254.63546562952507, (29, 2950): 254.91647802605522, (29, 2952): 254.66454305236954, (29, 2958): 254.59439944819766, (29, 2959): 254.7805071808925, (29, 2960): 255.36447264646085, (29, 2961): 255.11645974611395, (29, 2963): 254.40891275021352, (29, 2968): 254.60021451187964, (29, 2976): 254.3108833623617, (29, 2981): 249.86505891364862, (29, 2982): 249.78867148370458, (29, 2984): 249.5532136816429, (29, 3003): 249.18356983703157, (29, 3046): 245.21136818085745, (29, 3050): 248.1109745416924, (29, 3051): 248.28522243780074, (29, 3053): 247.75972468142538, (29, 3069): 250.94255180272836, (29, 3071): 247.48686916625923, (29, 3080): 258.80244183999093, (29, 3199): 248.75762010498946, (29, 3200): 248.221708560337, (29, 3205): 251.75742336235808, (29, 3209): 248.5319229352152, (29, 3215): 248.22151183509357, (29, 3217): 247.51788273618956, (29, 3249): 248.24767233068428, (29, 3263): 253.54569290840104, (29, 3289): 249.8247822912135, (29, 3301): 250.0870371067476, (29, 3302): 249.7990408017177, (29, 3307): 249.47315093428142, (29, 3310): 250.39007993042722, (29, 3391): 252.91092630117217, (29, 3509): 134.12686196444844, (29, 3510): 133.61852190388544, (29, 3511): 133.90218624015534, (29, 3512): 133.5398029937118, (29, 3514): 133.60352770939525, (29, 3519): 135.5907069337642, (29, 3536): 134.92751665136592, (29, 3545): 135.6707202812679, (29, 3548): 134.82042415157386, (29, 3572): 135.28244750267064, (29, 3581): 134.85067280331688, (29, 3583): 134.27767315070884, (29, 3601): 136.63203961267365, (29, 3656): 136.02656452249764, (29, 3669): 135.5230094658676, (29, 3670): 135.9989801963869, (29, 3695): 133.19222654279037, (29, 3696): 133.5429893731567, (29, 3782): 134.11570759406155, (29, 3792): 133.68588483257108, (29, 3989): 93.18288025034657, (29, 4008): 96.03637132571443, (29, 4031): 96.29683308072049, (29, 4045): 94.85923088928931, (29, 4144): 94.61040908928602, (29, 4145): 91.3243901401285, (29, 4164): 93.40728673491353, (29, 4168): 92.31980095102058, (29, 4173): 92.0410519548782, (29, 4181): 90.30351008280905, (29, 4228): 89.10733043991637, (29, 4248): 87.7948698752413, (29, 4254): 70.60534402697681, (29, 4260): 70.80964612950153, (29, 4262): 71.71922883594294, (29, 4273): 71.59562338686787, (29, 4319): 61.3776918490998, (29, 4326): 61.088593360642435, (29, 4328): 61.24537890637359, (29, 4334): 61.749808021749246, (29, 4335): 61.500210650138975, (29, 4372): 77.13207476378207, (29, 4413): 86.32181436678911, (29, 4434): 76.44625399196445, (29, 4447): 76.42988735465097, (29, 4452): 76.72691224966034, (29, 4463): 69.39510838042719, (29, 4465): 69.33745731204618, (29, 4619): 90.54894618102246, (29, 4645): 91.44266909790447, (29, 4657): 91.63324264022035, (29, 4666): 91.45944630400933, (29, 4676): 92.43148785086268, (29, 4678): 92.45389311410285, (29, 4689): 92.28251619096665, (29, 4704): 97.2629350592997, (29, 4726): 117.71310116413393, (29, 4727): 117.37255796613988, (29, 4730): 116.68709544496092, (29, 4731): 117.04829107395493, (29, 4734): 116.48518368662468, (29, 4735): 116.30253717557768, (29, 4736): 116.58718270763188, (29, 4737): 116.18070472906201, (29, 4738): 116.35602393642297, (29, 4756): 116.77172082428447, (29, 4760): 114.37589170269746, (29, 4761): 114.29486680783356, (29, 4762): 114.07689629275052, (29, 4765): 114.62569587317249, (29, 4773): 118.24664891406667, (29, 4774): 118.16411998376462, (29, 4790): 117.98742594483731, (29, 4795): 117.63488614981848, (29, 4799): 118.4285554606533, (29, 4801): 119.44464330152064, (29, 4804): 117.47521142627083, (29, 4805): 117.18892951197023, (29, 4806): 118.36216608409184, (29, 4815): 118.23223159261296, (29, 4816): 118.9827028838063, (29, 4817): 119.40763044127112, (29, 4826): 118.82152856322739, (29, 4830): 118.44831429627118, (29, 4839): 115.38016618123228, (29, 4840): 115.79263761882929, (29, 4841): 115.16422043820333, (29, 4846): 114.8853845055964, (29, 4848): 115.02806850623512, (29, 4850): 115.37471014927048, (29, 4871): 110.42347979095685, (29, 4883): 113.67410435191617, (29, 4900): 111.69653296384232, (29, 4901): 111.44678883965084, (29, 4917): 95.16132928098244, (29, 4931): 93.02456864381737, (29, 4944): 95.22061755464325, (29, 4956): 93.60105300266292, (29, 4958): 93.90726248713005, (29, 4959): 93.75708803144352, (29, 4961): 93.88350967358474, (29, 4966): 93.2938174926309, (29, 5207): 90.98125258264044, (29, 5272): 37.42658315752676, (29, 5283): 38.342318350299614, (29, 5287): 40.83907154821317, (29, 5289): 41.27701276802051, (29, 5293): 36.58449990361243, (29, 5295): 39.02543330022636, (29, 5296): 39.61826273962518, (29, 5298): 39.934040652680636, (29, 5303): 41.180256955453345, (29, 5305): 38.189781963945265, (29, 5306): 38.47752603335914, (29, 5307): 37.803665475827614, (29, 5308): 38.797234864806455, (29, 5313): 37.93504070902496, (29, 5314): 38.23430884454751, (29, 5317): 39.235236458989746, (29, 5319): 40.50208429702323, (29, 5324): 39.53386963056953, (29, 5326): 38.874951958238476, (29, 5348): 38.8687954046535, (29, 5351): 40.45044018362189, (29, 5399): 42.69792044147306, (29, 5413): 43.03985639427849, (29, 5422): 42.520168500063455, (29, 5445): 40.86865274241906, (29, 5448): 40.07649543240278, (29, 5456): 40.594143246835465, (29, 5467): 41.51154396842229, (29, 5624): 30.59820791914162, (29, 5671): 50.155996724316374, (29, 5672): 48.92911682374428, (29, 5797): 64.38395862117808, (29, 5871): 59.800180178308146, (29, 5976): 51.10744623909607, (29, 6118): 199.8818714813616, (29, 6248): 212.43779065487047, (29, 6345): 38.813075715696726, (29, 6352): 40.81740453682031, (29, 6354): 38.084643037486224, (29, 6359): 38.14181665510006, (29, 6376): 41.554520097497736, (29, 6378): 38.36824037619866, (29, 6381): 38.60969791176837, (29, 6383): 39.0581802906371, (29, 6396): 40.59610389581129, (29, 6399): 39.319723476719794, (29, 6408): 40.31385819766054, (29, 6409): 38.21926248177759, (29, 6419): 39.8772070922271, (29, 6422): 39.15444046643064, (29, 6423): 39.25732474564792, (29, 6424): 36.972674815765224, (29, 6439): 36.98534343364748, (29, 6464): 37.18913295896174, (29, 6465): 37.78301686506883, (29, 6469): 38.36083466834625, (29, 6470): 38.67623953653775, (29, 6472): 37.6642394692861, (29, 6480): 36.106337143600044, (29, 6486): 32.870665009987995, (29, 6497): 33.857207700369884, (29, 6503): 34.775353791916736, (29, 6508): 35.85949345052762, (29, 6509): 34.899538208123225, (29, 6521): 34.98682160800729, (29, 6544): 33.90621410888935, (29, 6552): 36.7940639857014, (29, 6553): 36.99495828510664, (29, 6554): 37.217442690762184, (29, 6578): 36.636285209056794, (29, 6582): 35.582961223802634, (29, 6601): 36.2827069476833, (29, 6609): 35.8616783526168, (29, 6610): 35.52821343886322, (29, 6611): 36.1957941728994, (29, 6614): 36.72900016756969, (29, 6615): 36.4427913642211, (29, 6616): 35.29950578675786, (29, 6617): 35.72161455941512, (29, 6618): 34.47201762945118, (29, 6619): 36.74042114675981, (29, 6620): 34.85339045025656, (29, 6621): 34.94802052793376, (29, 6622): 35.209352855209666, (29, 6623): 36.26773037427273, (29, 6624): 35.97195336608492, (29, 6625): 36.242992297827115, (29, 6626): 36.942600672661406, (29, 6627): 37.15885501501933, (29, 6628): 34.44276514974356, (29, 6629): 35.38247396436822, (29, 6630): 37.10404772454986, (29, 6632): 35.64472397656029, (29, 6634): 37.025450710620994, (29, 6635): 35.252185514100105, (29, 6636): 35.136229436570304, (29, 6637): 35.593364632172026, (29, 6638): 36.66496978770174, (29, 6639): 36.88281909460995, (29, 6640): 36.855088219650014, (29, 6641): 34.60901693279499, (29, 6642): 36.369572744373095, (29, 6643): 37.276448901121015, (29, 6645): 36.51502612262978, (29, 6646): 34.88623631710752, (29, 6647): 36.475098988451656, (29, 6653): 36.58686336199067, (29, 6655): 37.02403900004853, (29, 6658): 36.869275937439255, (29, 6662): 36.06818209595014, (29, 6819): 44.62090348222091, (29, 6996): 34.703068575417944, (29, 7059): 31.15837154932662, (29, 7187): 31.374506641120735, (29, 7304): 42.67814385015001, (29, 7528): 31.389414943996403, (29, 7720): 17.136185549909733, (29, 7793): 14.620563269404295, (29, 7807): 15.374860963234854, (29, 7808): 14.052660780835364, (29, 7831): 31.505416666999135, (29, 7850): 31.92113300943454, (29, 7852): 32.95373979848867, (29, 8012): 21.267553834666522, (29, 8125): 12.5, (29, 8208): 16.155027904584465, (29, 8392): 22.85191350863615, (29, 8651): 62.21113436551129, (29, 9088): 52.218961971195434, (29, 9443): 64.65135449513255, (29, 9444): 64.01401522580355, (29, 9828): 83.04188753321112, (29, 9868): 83.78912426376921, (29, 10180): 12.5, (29, 10256): 12.5, (29, 10276): 12.5, (29, 10378): 12.5, (29, 10676): 12.5, (29, 10714): 17.070276761700075, (29, 10730): 12.5, (29, 10862): 80.32719995395293, (29, 10881): 80.63715082514082, (29, 10883): 80.8586347006469, (29, 10885): 80.19972967293589, (29, 10891): 81.21130239251737, (29, 10909): 80.57059584621568, (29, 10911): 79.98497947225924, (29, 10913): 80.115650176044, (29, 10915): 79.78743571299141, (29, 10919): 79.55824474901482, (29, 11037): 85.90165556710532, (29, 11039): 82.9393486144361, (29, 11516): 128.01020399405996, (29, 11856): 62.005355976997954, (29, 11857): 61.384130936813776, (29, 11861): 61.7024173672185, (29, 11881): 61.56033416642934, (29, 11902): 59.73641369081601, (29, 11911): 59.66949886261536, (29, 11914): 59.80523280997057, (29, 11922): 61.06881412238962, (29, 11924): 61.56358292363676, (29, 11926): 61.054064718837665, (29, 11950): 62.37778140630925, (29, 11963): 64.04584404968416, (29, 11983): 63.38265064246328, (29, 11985): 64.86154531602982, (29, 12009): 64.92860608277964, (29, 12010): 63.64682323463955, (29, 12018): 63.897650712398395, (29, 12020): 64.15857933003751, (29, 12021): 64.39977272441766, (29, 12024): 65.53152397825622, (29, 12025): 65.06625557559028, (29, 12027): 64.81821168621725, (29, 12031): 63.44666793266942, (29, 12032): 63.77492395286632, (29, 12035): 64.94972072098544, (29, 12041): 64.79003985669233, (29, 12045): 49.601690267482525, (29, 12145): 57.22449955750765, (29, 12275): 95.39014531461017, (29, 12294): 93.31407257951636, (29, 12358): 102.86774510816362, (29, 12463): 107.08026378366564, (29, 12465): 107.02335224556916, (29, 12482): 107.86259638154395, (29, 12503): 107.8172869933302, (29, 12506): 108.21104450917305, (29, 12549): 106.5844205325657, (29, 12559): 106.43586081321563, (29, 12569): 107.03349281986422, (29, 12572): 107.31423253431842, (29, 12574): 106.64207906367191, (29, 12576): 106.83679504543124, (29, 12591): 106.33368422065809, (29, 12608): 108.44090824464855, (29, 12696): 104.29315441857521, (29, 12710): 106.01582906869535, (29, 12728): 105.49073219398323, (29, 12766): 48.639757198698426, (29, 12771): 43.37957632430004, (29, 12790): 43.27756874394231, (29, 12795): 43.51219061317724, (29, 12797): 39.17834314002688, (29, 12798): 39.31054254913799, (29, 12811): 41.27966561180128, (29, 12830): 41.28387182787636, (29, 12848): 40.24753854256784, (29, 12850): 39.594301251457665, (29, 12852): 40.77425731981577, (29, 12854): 40.48570666840189, (29, 12859): 40.19144426309209, (29, 12861): 39.29954860323349, (29, 12865): 42.25885718081514, (29, 12866): 41.697777464555315, (29, 12867): 42.68092516085816, (29, 12874): 42.25865739046255, (29, 12875): 42.32335841259502, (29, 12881): 41.83681202151044, (29, 12883): 42.16106456074469, (29, 12885): 42.62146158274539, (29, 12888): 41.72100961489844, (29, 12889): 41.37232943256711, (29, 12892): 42.47948162934356, (29, 12893): 42.01296929317138, (29, 12896): 41.910655135950975, (29, 12906): 43.50768163489804, (29, 13018): 48.70448528504922, (29, 13071): 50.43032328629048, (29, 13131): 42.080877586052154, (29, 13146): 41.91870497705104, (29, 13159): 49.30138314523384, (29, 13193): 41.35592691305242, (29, 13198): 36.96330218229495, (29, 13292): 37.869133726404954, (29, 13296): 35.544689124973466, (29, 13406): 41.645984250525984, (29, 13407): 42.04100791879346, (29, 13417): 45.2050172273326, (29, 13418): 45.73636958843895, (29, 13438): 43.4054834543098, (29, 13442): 42.396590622675916, (29, 13443): 42.48564889986761, (29, 13764): 78.88274871028032, (29, 13766): 78.44057994177048, (29, 13771): 79.8243824574712, (29, 13783): 77.67831490074114, (29, 13784): 77.54838525456584, (29, 13792): 82.10578926833969, (29, 13824): 78.17738696462368, (29, 14017): 70.04024430565649, (29, 14870): 67.15491194892635, (29, 14997): 34.360988008758405, (29, 15000): 34.18165021989936, (29, 15003): 33.62484508090419, (29, 15006): 33.14187105358039, (29, 15007): 32.66776000274098, (29, 15056): 32.33907365761615, (29, 15063): 32.68671675254349, (29, 15069): 32.7293034535131, (29, 15076): 32.49375777591109, (29, 15086): 34.120924697241186, (29, 15087): 34.41604497396741, (29, 15111): 35.934532324665426, (29, 15116): 35.0476370053983, (29, 15722): 47.32518265705861, (29, 15998): 54.73129081492813, (29, 16073): 166.37800405014826, (29, 16939): 209.79772874463532, (29, 16940): 209.11656353236816, (29, 16951): 210.00444774135747, (29, 16963): 210.04202392977857, (29, 16965): 210.82159016657673, (29, 16969): 210.69126147258416, (29, 16970): 210.30234608371643, (29, 16971): 209.59580178469832, (29, 16973): 209.58920922583602, (29, 16974): 211.1739006033335, (29, 16976): 210.3314741993538, (29, 16978): 209.80100932720907, (29, 16980): 210.558319868994, (29, 16982): 211.21095964105774, (29, 17045): 236.77471940418525, (29, 17048): 237.7104319951823, (29, 17304): 83.19739200323912, (29, 17305): 83.03889715766287, (29, 17330): 83.37848951689284, (29, 17334): 82.25359690070812, (29, 17343): 84.10615542207162, (29, 17345): 82.53351031548222, (29, 17347): 83.52398476939923, (29, 17351): 81.04319936030204, (29, 17372): 82.27118928589688, (29, 17373): 84.00592731326867, (29, 17377): 84.15343427210385, (29, 17382): 83.09004001968255, (29, 17383): 83.18274504192536, (29, 17389): 82.58024555607525, (29, 17400): 83.61198745583336, (29, 17401): 83.5417603858756, (29, 17402): 83.70483802633687, (29, 17403): 83.83611930479368, (29, 17440): 82.94936068364164, (29, 17455): 84.13013850614574, (29, 17491): 84.47229311705433, (29, 17507): 80.9367257439561, (29, 17509): 81.4483470179284, (29, 17590): 81.0075335450108, (29, 17615): 75.94377636567974, (29, 17642): 76.65381060876712, (29, 17643): 76.70062967158131, (29, 17668): 75.86146925230507, (29, 17721): 73.99214889340435, (29, 17754): 79.38388575099964, (29, 17769): 80.82009313405143, (29, 17776): 79.01212596022881, (29, 17804): 81.71884273116069, (29, 17809): 82.3020910869856, (29, 17824): 81.75998142966709, (29, 17837): 80.87567070708837, (29, 17838): 81.10486838398452, (29, 17862): 80.75444191088812, (29, 17866): 81.90837005797754, (29, 17872): 80.23563907256559, (29, 17873): 79.39338586946197, (29, 17881): 80.71170159967832, (29, 17947): 153.28141543092215, (29, 17951): 152.08700750307813, (29, 17953): 151.81657613514707, (29, 17954): 151.8726220254197, (29, 17959): 153.10841396818262, (29, 17963): 152.76239565796513, (29, 18000): 146.5808936289555, (29, 18001): 146.75941374044706, (29, 18111): 162.65688720179992, (29, 18148): 130.94460525362362, (29, 18166): 143.073534093916, (29, 18189): 154.66663016348335, (29, 18239): 84.18326704980606, (29, 18240): 84.2077570576916, (29, 18245): 84.25380049249794, (29, 18247): 84.16024093121217, (29, 18251): 84.28993115867773, (29, 18256): 84.46737907677328, (29, 18258): 84.34001513479045, (29, 18259): 84.38342310801809, (29, 18260): 84.4640517252377, (29, 18262): 84.59386592669838, (29, 18263): 84.52369150707811, (29, 18264): 84.60177194216325, (29, 18266): 84.66564518845944, (29, 18267): 84.73774516828979, (29, 18268): 84.7852686499785, (29, 18269): 84.93258737913264, (29, 18275): 84.86321152432036, (29, 18285): 84.56266291488849, (29, 18308): 83.02994535988242, (29, 18313): 82.59864082175885, (29, 18314): 82.8903885304354, (29, 18315): 84.83585984389318, (29, 18316): 84.86778723337585, (29, 18317): 84.93936539764783, (29, 18320): 84.94426012052382, (29, 18321): 85.00302424466021, (29, 18322): 85.1070303799217, (29, 18324): 85.1302100530538, (29, 18325): 85.39365505962871, (29, 18326): 85.29352494095716, (29, 18327): 85.0412848326194, (29, 18329): 85.46409907238471, (29, 18330): 85.46651568947927, (29, 18331): 85.26883207722972, (29, 18332): 85.08764449850858, (29, 18333): 85.4004635392673, (29, 18336): 85.1881617953947, (29, 18337): 85.25031561073511, (29, 18403): 85.36098799314806, (29, 18432): 83.14935047698185, (29, 18451): 84.63533082657956, (29, 18466): 86.04638399691812, (29, 18481): 84.79118246380158, (29, 18483): 84.82127168989734, (29, 18484): 84.65314314894468, (29, 18485): 84.11691234495875, (29, 18486): 84.39924244601316, (29, 18487): 84.02613027571029, (29, 18489): 84.46003571009871, (29, 18490): 84.71536531252778, (29, 18491): 84.8740057585207, (29, 18492): 83.71197532532655, (29, 18493): 84.30738750674038, (29, 18494): 84.41993404564177, (29, 18495): 84.5926783615694, (29, 18496): 84.45090018658472, (29, 18497): 83.91284423383159, (29, 18498): 84.11146648527226, (29, 18499): 84.36988757757142, (29, 18501): 84.12996133561472, (29, 18502): 83.96124546461398, (29, 18503): 83.86816739755928, (29, 18504): 84.55358276734592, (29, 18506): 84.0692073439907, (29, 18507): 83.89163845739391, (29, 18508): 84.3047730574458, (29, 18509): 84.27968288715253, (29, 18510): 83.8306323553575, (29, 18511): 84.29666566428752, (29, 18512): 84.1581739857921, (29, 18515): 84.52652851393655, (29, 18516): 84.44138272113919, (29, 18517): 84.18608804842894, (29, 18518): 84.60358179513631, (29, 18519): 84.6066375030272, (29, 18520): 84.29191096898461, (29, 18522): 85.3643340737535, (29, 18523): 85.36604581329564, (29, 18532): 85.54404233872604, (29, 18535): 85.14011826353247, (29, 18537): 84.91535386110533, (29, 18539): 84.94483688273928, (29, 18540): 84.9525349778548, (29, 18541): 85.04802893710585, (29, 18542): 85.1118788688723, (29, 18543): 84.78126996263322, (29, 18546): 84.88170506726415, (29, 18555): 85.23165461900358, (29, 18556): 85.27290556516036, (29, 18565): 85.47307420916319, (29, 18567): 85.51045065345373, (29, 18568): 85.34721870163422, (29, 18577): 86.7326994047441, (29, 18583): 86.59019274966055, (29, 18605): 86.99073065732358, (29, 18608): 85.49876836208855, (29, 18616): 88.27711175293341, (29, 18618): 89.3182122682584, (29, 18625): 89.18090460647126, (29, 18645): 88.31336334132097, (29, 18646): 88.48433153348515, (29, 18653): 87.33546835991591, (29, 18654): 88.20997633247254, (29, 18655): 87.58563012210489, (29, 18666): 91.56063767249181, (29, 18837): 92.07749254783906, (29, 18974): 85.51325567506524, (29, 18999): 86.92082025052729, (29, 19000): 87.25542623759694, (29, 19174): 75.46510916132031, (29, 19342): 83.00420591362258, (29, 19455): 74.95377965855708, (29, 19555): 62.271435751342146, (29, 19564): 65.4247062527796, (29, 19573): 64.32254453595044, (29, 19586): 63.677897732689694, (29, 19605): 63.53006670197853, (29, 19611): 64.18586244980654, (29, 19614): 63.257834362830884, (29, 19641): 71.52172242709977, (29, 19702): 72.05290554531018, (29, 19713): 71.30409481421925, (29, 19731): 56.57998657258805, (29, 19819): 73.69945405042172, (29, 19893): 42.89743346288285, (29, 19899): 47.58155264938591, (29, 19929): 43.956832868439975, (29, 19951): 52.636629288674314, (29, 19962): 44.98275894005443, (29, 19970): 46.275972931522396, (29, 19971): 46.44076279931134, (29, 19972): 45.81117390650298, (29, 19975): 45.37665120054493, (29, 19978): 53.84833898512033, (29, 19987): 53.92024412774988, (29, 19989): 51.563434408879125, (29, 20039): 54.31875885193122, (29, 20043): 55.206674333925164, (29, 20047): 54.37668964970829, (29, 20052): 51.85057900725005, (29, 20054): 52.09545822591843, (29, 20085): 63.312828561427246, (29, 20104): 64.0282017249721, (29, 20132): 59.71747776970915, (29, 20203): 44.15595012660114, (29, 20280): 43.91443342327929, (29, 20285): 44.00357337083737, (29, 20290): 44.18174673275643, (29, 20297): 43.311334990438816, (29, 20309): 55.50391197183676, (29, 20453): 66.77467696951386, (29, 20485): 37.922853979658285, (29, 20520): 35.69729215825592, (29, 20526): 35.716284360748695, (29, 20698): 106.98283431976415, (29, 20868): 126.07007907380299, (29, 21042): 24.56980718370005, (29, 21057): 28.757452063210707, (29, 21066): 26.008009945441415, (29, 21075): 26.198688558434835, (29, 21093): 23.909639873187952, (29, 21098): 25.68771369788278, (29, 21127): 24.38578536925389, (29, 21130): 24.70832975543903, (29, 21144): 25.482504942771744, (29, 21146): 24.12274295639287, (29, 21147): 25.688368819729742, (29, 21148): 26.08180680023112, (29, 21153): 28.237620015344724, (29, 21293): 30.499441939210524, (29, 21426): 38.01386673489589, (29, 21442): 43.7855402349424, (29, 21451): 44.303500248265415, (29, 21466): 40.38417043873377, (29, 21469): 40.79464874255696, (29, 21471): 40.19997407925622, (29, 21473): 40.42263339008286, (29, 21475): 40.09848079709198, (29, 21482): 41.42485025210419, (29, 21484): 41.144642224182995, (29, 21488): 41.00242228940917, (29, 21494): 39.57806409779055, (29, 21498): 40.01655355819348, (29, 21500): 38.91652887865015, (29, 21514): 38.16224700649479, (29, 21537): 37.66765809209432, (29, 21662): 37.43928407274371, (29, 21691): 35.19169518420974, (29, 21757): 35.65146586262923, (29, 21777): 14.032591740833558, (29, 21778): 13.610999580777488, (29, 21779): 13.29453961561696, (29, 21790): 15.116452400950356, (29, 21802): 14.053874571714285, (29, 21824): 14.063895499183408, (29, 21874): 12.753251078680726, (29, 21879): 12.5, (29, 21983): 18.82768688272147, (29, 22002): 21.73585244267984, (29, 22132): 29.60105786593718, (29, 22261): 89.47906678198477, (29, 22298): 88.05385695652754, (29, 22339): 97.25222758822274, (29, 22508): 74.65153179293229, (29, 22841): 254.3408340747945, (29, 22842): 254.3173301667324, (29, 22874): 252.42138652324275, (29, 22941): 252.69856349340776, (29, 22956): 253.7762980503358, (29, 22960): 254.16623656544033, (29, 22968): 254.8775115397019, (29, 22970): 255.23410283345078, (29, 22974): 255.5379211228449, (29, 22980): 256.8580825668526, (29, 23025): 256.3754626383454, (29, 23028): 256.0076975084294, (29, 23081): 257.79027439424897, (29, 23104): 254.79869525820345, (29, 23147): 244.14243931798285, (29, 23298): 46.75943834528273, (29, 23376): 44.72644274916306, (29, 23381): 41.97728152282525, (29, 23529): 46.86595941045493, (29, 23556): 45.851487510406635, (29, 23718): 46.85788730334604, (29, 24001): 59.263562976897866, (29, 24094): 61.064283260491116, (29, 24129): 63.17082436399388, (29, 24174): 58.071639561752086, (29, 24235): 62.33790881972693, (29, 24259): 64.78806685897985, (29, 24260): 64.57052658752065, (29, 24261): 64.17888140541572, (29, 24305): 67.38365132708726, (29, 24306): 67.7047482761087, (29, 24307): 67.139450795622, (29, 24308): 65.91104241320969, (29, 24498): 74.07144875237819, (29, 24499): 74.08312941814505, (29, 24500): 73.73249938113128, (29, 24668): 73.1077967417729, (29, 24711): 75.95504470902243, (29, 24756): 76.83493758911854, (29, 24788): 77.65364736610823, (29, 24809): 74.80961989733785, (29, 24813): 75.73548020335897, (29, 24821): 75.44916745099864, (29, 24825): 75.58239103398745, (29, 24832): 74.67969784025337, (29, 24833): 75.06735241487466, (29, 24835): 75.42991363380894, (29, 24837): 76.1022221879926, (29, 24840): 74.59146423002105, (29, 24841): 75.24910614120844, (29, 24844): 74.57115059256273, (29, 24845): 75.07412835659453, (29, 24846): 74.83063870938047, (29, 24849): 75.02381362236811, (29, 24850): 75.80644519819161, (29, 24863): 70.69387914964277, (29, 24866): 71.40235849363944, (29, 24885): 72.0932905957207, (29, 24886): 72.06936979692814, (29, 24889): 73.8987108806974, (29, 24903): 74.62825470227239, (29, 24909): 72.31115555097591, (29, 24999): 103.5662331980532, (29, 25019): 103.15088327206277, (29, 25028): 103.06849432887604, (29, 25137): 49.50417109418092, (29, 25145): 50.130425781513274, (29, 25208): 61.58760273683266, (29, 25233): 60.86767069970246, (29, 25371): 46.95595083423936, (29, 25377): 44.282633254315705, (29, 25828): 20.03918801669933, (29, 25851): 18.685756998837366, (29, 25874): 17.619425657442847, (29, 25898): 20.885958307216928, (29, 25946): 19.928362132401265, (29, 26047): 28.223260034871736, (29, 26066): 26.598773664803055, (29, 26197): 23.36348680827092, (29, 26212): 39.72466565161015, (29, 26253): 41.94122181094608, (29, 26254): 40.88760587969196, (29, 26257): 40.78109531574215, (29, 26258): 41.68611899978942, (29, 26260): 41.16916337871388, (29, 26266): 40.524698624383234, (29, 26267): 40.128914434743976, (29, 26271): 40.29134547629444, (29, 26304): 31.884598126218084, (29, 26305): 31.439352975166138, (29, 26363): 24.688651008553254, (29, 26441): 93.81727117910215, (29, 26442): 93.57000746799865, (29, 26450): 92.37792867339881, (29, 26459): 92.3018931091006, (29, 26462): 92.47932707203657, (29, 26467): 95.9749095949359, (29, 26471): 94.98371871888183, (29, 26472): 94.87708804558105, (29, 26473): 94.83436381794843, (29, 26476): 94.26144596011179, (29, 26485): 92.88568894258822, (29, 26493): 92.91499312849176, (29, 26524): 93.01661716637913, (29, 26525): 92.87132419046658, (29, 26556): 94.51174515509956, (29, 26560): 94.41684655861646, (29, 26561): 93.66756061397211, (29, 26564): 94.18468502698074, (29, 26569): 93.47536970169735, (29, 26570): 93.1660967820463, (29, 26573): 93.34916471086031, (29, 26581): 93.31640196630892, (29, 26583): 93.05829122186732, (29, 26593): 93.32076728379933, (29, 26837): 96.20575572612955, (29, 26844): 97.00713949471512, (29, 26863): 95.2567828778254, (29, 26893): 97.55839519433496, (29, 26902): 98.64458983053308, (29, 26905): 97.54926296328568, (29, 26912): 98.3956045317392, (29, 26921): 96.35932477764212, (29, 26922): 94.19651265676855, (29, 27212): 103.6252707094611, (29, 27218): 102.81127914587505, (29, 27239): 105.13470985057788, (29, 27257): 104.28073320523997, (29, 27274): 105.41816289589357, (29, 27279): 105.18907906712714, (29, 27282): 104.28468463321265, (29, 27283): 104.75387716687204, (29, 27285): 105.7933990233042, (29, 27286): 104.86609503379182, (29, 27290): 103.50224953759236, (29, 27295): 103.03170795113986, (29, 27300): 105.59684374959225, (29, 27344): 102.92051596261128, (29, 27366): 103.89237888754464, (29, 27383): 105.75488837397386, (29, 27398): 106.99506380287822, (29, 27406): 106.13742102925063, (29, 27407): 106.45076718628927, (29, 27426): 105.68015625524177, (29, 27432): 101.6455388186797, (29, 27460): 104.23201350787633, (29, 27523): 103.46272856303153, (29, 27545): 120.36083658731287, (29, 27602): 140.64231995838207, (29, 27606): 141.06419240161333, (29, 27646): 118.88674053093158, (29, 27667): 122.99439830312743, (29, 27672): 123.23222366048307, (29, 27674): 122.51805014490014, (29, 27688): 123.19590524043335, (29, 27692): 123.91720849865916, (29, 27693): 123.29760342639949, (29, 27705): 123.24050588080591, (29, 27712): 123.52468638331962, (29, 27786): 142.8162143831128, (29, 27790): 141.03532773649684, (29, 27791): 140.92183685731197, (29, 27795): 141.62690121123484, (29, 27801): 140.24481770600772, (29, 27813): 143.39075262332938, (29, 27816): 142.74230776995833, (29, 27823): 140.19780494751103, (29, 27830): 141.9549379442632, (29, 27884): 111.77795269548227, (29, 27885): 117.12113719155283, (29, 27896): 113.90178645559493, (29, 27919): 113.7039211775369, (29, 27922): 114.3341083438094, (29, 27930): 112.61808664455305, (29, 27934): 112.8022529770987, (29, 27935): 112.930314132993, (29, 27948): 137.56145292396505, (29, 27951): 138.93346290371937, (29, 28061): 119.27813248548665, (29, 28290): 161.77750816386404, (29, 28292): 162.68214169509494, (29, 28293): 161.95495452352213, (29, 28295): 161.5974871486023, (29, 28296): 161.73931547352086, (29, 28297): 161.2997306371834, (29, 28302): 160.99706156819315, (29, 28310): 182.07758533177963, (29, 28313): 182.98975282116072, (29, 28372): 182.6493499060721, (29, 28398): 182.75278876503904, (29, 28399): 182.49831143878507, (29, 28400): 182.9704483224846, (29, 28401): 181.67409645088975, (29, 28445): 182.71033557377825, (29, 28475): 180.410539318465, (29, 28885): 59.8066435557861, (29, 28886): 59.311606109393786, (29, 28915): 59.29784640774925, (29, 28916): 59.07029536540119, (29, 28917): 58.775662646232554, (29, 28921): 60.63635983409425, (29, 28931): 60.42684514679249, (29, 28945): 57.30401231165028, (29, 28982): 58.13389257832905, (29, 29219): 59.10051871345588, (29, 29228): 57.34124662610526, (29, 29246): 68.5093593653293, (29, 29248): 68.29462912528003, (29, 29282): 65.90789551962114, (29, 29290): 69.76105804488148, (29, 29291): 69.25876655255247, (29, 29292): 69.71649366153673, (29, 29293): 68.78757379610019, (29, 29294): 69.49198380998588, (29, 29298): 68.83497670612032, (29, 29299): 68.7339536246993, (29, 29304): 67.91686282755349, (29, 29317): 65.73227360205435, (29, 29323): 65.56691519308701, (29, 29330): 66.6114571940553, (29, 29331): 67.15563141701836, (29, 29344): 59.01755288223779, (29, 29445): 38.33360919806305, (29, 29724): 251.9934926975395, (29, 29738): 252.34378922694964, (29, 29745): 251.34730526199388, (29, 29748): 251.67957178385674, (29, 29750): 252.30760976203453, (29, 29759): 251.18316563039946, (29, 29772): 252.4800122834927, (29, 29781): 252.2006497631312, (29, 29784): 251.9224718134469, (29, 29790): 252.50613542815472, (29, 29811): 251.8265800751718, (29, 29817): 254.57574923861324, (29, 29818): 254.3064475287878, (29, 29929): 251.14448920048304, (29, 30039): 255.36121918710404, (29, 30066): 252.21096622317316, (29, 30116): 240.55193795602216, (29, 30238): 223.28771684119238, (29, 30248): 231.3926156588044, (29, 30260): 231.5529336014025, (29, 30545): 55.25087873736202, (29, 30733): 38.862332867451805, (29, 30756): 30.77117634988651, (29, 30921): 40.50774177945003, (29, 31079): 52.02244111550862, (29, 31149): 46.236501295927745, (29, 31154): 47.20115923388306, (29, 31160): 46.11131815464534, (29, 31163): 47.19606456257406, (29, 31189): 45.84442961755823, (29, 31215): 46.72642591676173, (29, 31259): 50.97538926185695, (29, 31262): 50.674622375708424, (29, 31430): 55.04905914279302, (29, 31568): 62.92926307002878, (29, 31751): 53.75449441229197, (31, 109): 234.07804758294444, (31, 872): 46.80179811174707, (31, 873): 45.893548856298004, (31, 877): 45.998328622522656, (31, 879): 45.84053038035537, (31, 884): 46.247216255934724, (31, 889): 45.780420258877896, (31, 891): 46.60985783577158, (31, 892): 45.18389063457277, (31, 894): 45.39565829773646, (31, 896): 46.66807633215473, (31, 903): 45.69964696876804, (31, 909): 48.01657310196919, (31, 910): 47.877537364346786, (31, 912): 48.423040745650304, (31, 913): 48.94428064546224, (31, 916): 49.488860672994505, (31, 926): 47.88126179882489, (31, 927): 48.23519837172368, (31, 948): 46.97748163224316, (31, 961): 47.383329327044564, (31, 962): 47.43693640961021, (31, 963): 47.44825282727459, (31, 967): 45.40770396637721, (31, 974): 45.36950318550074, (31, 998): 44.85721984187547, (31, 1014): 29.280624650063995, (31, 1086): 56.51434399061481, (31, 1087): 57.68551689840255, (31, 1089): 57.88169521481234, (31, 1090): 57.448017754098636, (31, 1092): 56.26234715078601, (31, 1097): 56.95707438903285, (31, 1107): 56.36368800936841, (31, 1387): 190.72775893725975, (31, 1554): 202.52379791959598, (31, 1827): 12.5, (31, 1828): 12.5, (31, 1829): 12.5, (31, 1830): 12.5, (31, 1831): 12.5, (31, 1832): 12.5, (31, 1833): 12.5, (31, 1836): 12.5, (31, 1841): 12.5, (31, 1843): 12.5, (31, 1844): 12.5, (31, 1845): 12.5, (31, 1847): 12.5, (31, 1848): 12.5, (31, 1849): 12.5, (31, 1850): 12.5, (31, 1851): 12.5, (31, 1852): 12.5, (31, 1854): 12.5, (31, 1856): 12.5, (31, 1857): 12.5, (31, 1858): 12.5, (31, 1861): 12.5, (31, 1866): 12.5, (31, 1867): 12.5, (31, 1868): 12.5, (31, 1870): 12.5, (31, 1871): 12.5, (31, 1875): 12.5, (31, 1880): 12.5, (31, 1882): 12.5, (31, 1883): 12.5, (31, 1889): 12.5, (31, 1893): 12.5, (31, 1894): 12.5, (31, 1899): 12.5, (31, 1900): 12.5, (31, 1902): 12.5, (31, 1905): 12.5, (31, 1907): 12.5, (31, 1910): 12.5, (31, 1917): 12.5, (31, 1920): 12.5, (31, 1935): 12.5, (31, 1937): 12.5, (31, 1946): 12.5, (31, 1949): 12.5, (31, 1950): 12.5, (31, 1951): 12.5, (31, 1952): 12.5, (31, 1953): 12.5, (31, 1954): 12.5, (31, 1958): 12.5, (31, 1960): 12.5, (31, 1968): 12.5, (31, 1969): 12.5, (31, 1974): 12.5, (31, 1975): 12.5, (31, 1979): 12.5, (31, 1980): 12.5, (31, 1981): 12.5, (31, 1985): 12.5, (31, 1994): 12.5, (31, 2011): 12.5, (31, 2019): 12.5, (31, 2020): 12.5, (31, 2029): 12.5, (31, 2030): 12.5, (31, 2032): 12.5, (31, 2033): 12.5, (31, 2034): 12.5, (31, 2036): 12.5, (31, 2037): 12.5, (31, 2038): 12.5, (31, 2042): 12.5, (31, 2050): 12.5, (31, 2051): 12.5, (31, 2053): 12.5, (31, 2054): 12.5, (31, 2066): 12.5, (31, 2067): 12.5, (31, 2071): 12.5, (31, 2072): 12.5, (31, 2073): 12.5, (31, 2074): 12.5, (31, 2080): 12.5, (31, 2082): 12.5, (31, 2083): 12.5, (31, 2089): 12.5, (31, 2090): 12.5, (31, 2092): 12.5, (31, 2098): 12.5, (31, 2099): 12.5, (31, 2101): 12.5, (31, 2102): 12.5, (31, 2103): 12.5, (31, 2104): 12.5, (31, 2106): 12.5, (31, 2112): 12.5, (31, 2113): 12.5, (31, 2114): 12.5, (31, 2117): 12.5, (31, 2123): 15.22339184010633, (31, 2124): 15.168603966312824, (31, 2134): 14.357019490154938, (31, 2138): 14.560403732414711, (31, 2141): 14.633924811842009, (31, 2148): 12.5, (31, 2150): 14.655083131823911, (31, 2151): 14.28381721334407, (31, 2152): 14.453136718375658, (31, 2153): 12.5, (31, 2154): 12.5, (31, 2155): 12.5, (31, 2156): 12.5, (31, 2157): 12.5, (31, 2160): 12.609272442404729, (31, 2161): 14.101493687445437, (31, 2162): 12.5, (31, 2163): 12.5, (31, 2164): 12.5, (31, 2168): 12.70309022242189, (31, 2172): 12.5, (31, 2174): 13.82045168762809, (31, 2178): 12.5, (31, 2179): 12.5, (31, 2183): 14.114218299572908, (31, 2185): 13.870540791709569, (31, 2186): 14.046191117636779, (31, 2190): 13.025465791677764, (31, 2192): 13.251501371733703, (31, 2193): 14.232999775292315, (31, 2194): 14.467903870987934, (31, 2195): 13.992347386057382, (31, 2197): 12.949301840014705, (31, 2205): 12.578960802666785, (31, 2207): 12.5, (31, 2208): 12.5, (31, 2212): 15.303151746003993, (31, 2214): 15.20223593203428, (31, 2225): 13.355381660976276, (31, 2231): 22.69795188992751, (31, 2278): 12.5, (31, 2284): 12.5, (31, 2285): 12.5, (31, 2291): 12.5, (31, 2292): 12.5, (31, 2307): 12.5, (31, 2313): 12.5, (31, 2317): 12.5, (31, 2319): 12.5, (31, 2321): 12.5, (31, 2323): 12.5, (31, 2326): 12.5, (31, 2327): 12.5, (31, 2329): 12.5, (31, 2330): 12.5, (31, 2332): 12.5, (31, 2344): 12.5, (31, 2346): 12.5, (31, 2361): 12.5, (31, 2368): 12.5, (31, 2374): 12.5, (31, 2375): 12.5, (31, 2377): 12.5, (31, 2378): 12.5, (31, 2379): 12.5, (31, 2380): 12.5, (31, 2383): 12.5, (31, 2385): 12.5, (31, 2395): 12.5, (31, 2397): 12.5, (31, 2398): 12.5, (31, 2399): 12.5, (31, 2400): 12.5, (31, 2402): 12.5, (31, 2403): 12.5, (31, 2404): 12.5, (31, 2405): 12.5, (31, 2407): 12.5, (31, 2408): 12.5, (31, 2409): 12.5, (31, 2411): 12.5, (31, 2412): 12.5, (31, 2413): 12.5, (31, 2414): 12.5, (31, 2422): 12.5, (31, 2424): 12.5, (31, 2426): 12.5, (31, 2433): 12.5, (31, 2436): 12.5, (31, 2437): 12.5, (31, 2440): 12.5, (31, 2445): 12.5, (31, 2447): 12.5, (31, 2454): 12.5, (31, 2455): 12.5, (31, 2460): 12.5, (31, 2461): 12.5, (31, 2471): 12.684665005151366, (31, 2492): 23.44142891312735, (31, 2511): 19.62008529316525, (31, 2523): 21.56604161732146, (31, 2525): 22.343812214542545, (31, 2535): 13.59181697030758, (31, 2537): 13.653131976314311, (31, 2538): 13.170058209672742, (31, 2539): 15.26218807540277, (31, 2540): 13.633244079356048, (31, 2542): 14.378503407068594, (31, 2559): 17.288985004512295, (31, 2575): 18.360863204467062, (31, 2599): 12.5, (31, 2600): 12.5, (31, 2607): 12.5, (31, 2627): 27.700379588596128, (31, 2647): 29.776578265648954, (31, 2674): 27.128736991046086, (31, 2681): 28.164008560008213, (31, 2683): 27.971863961238327, (31, 2686): 27.07136751887864, (31, 2689): 34.568939914264256, (31, 2690): 34.85886083975839, (31, 2713): 43.95029589292214, (31, 2714): 45.10934827058956, (31, 2715): 45.2622799916355, (31, 2739): 44.825986861823644, (31, 2740): 41.02414583033711, (31, 2741): 40.89637539152401, (31, 2749): 45.69302156430039, (31, 2750): 45.376850610551315, (31, 2752): 45.32029273256545, (31, 2755): 45.6708466332805, (31, 2758): 45.93996000941166, (31, 2759): 45.77755497698414, (31, 2769): 45.18546739375239, (31, 2771): 42.012506991030854, (31, 2779): 44.71564476520935, (31, 2784): 44.301249990772945, (31, 2800): 47.247297062094766, (31, 2802): 42.151991170331456, (31, 2803): 41.76040826101092, (31, 2804): 41.52753833736437, (31, 2805): 43.2888725529733, (31, 2807): 42.94068773442334, (31, 2809): 43.64150606445686, (31, 2812): 41.85271880074301, (31, 2814): 45.842404633688496, (31, 2817): 48.92546643174255, (31, 2819): 42.132667892392114, (31, 2823): 44.90706484548825, (31, 2832): 43.957131051350565, (31, 2836): 43.237298964958846, (31, 2839): 42.59515970567849, (31, 2841): 47.410264178674936, (31, 2843): 46.814077025689514, (31, 2846): 44.75161547249904, (31, 2849): 44.642466883333164, (31, 2852): 44.25905895396082, (31, 2853): 44.84011032370983, (31, 2876): 46.48857064388295, (31, 2877): 47.31728392285557, (31, 2885): 50.69078782210099, (31, 2918): 40.06607643708915, (31, 2921): 40.73758291487395, (31, 2925): 36.5149384792037, (31, 2926): 34.48590110886909, (31, 2930): 40.80294037407445, (31, 2931): 37.55846967110132, (31, 2938): 40.652623988941095, (31, 2940): 38.75880888936518, (31, 2947): 37.04234957853688, (31, 2949): 39.46602430000021, (31, 2950): 40.162719214443, (31, 2952): 40.04765300709835, (31, 2958): 39.784103627069854, (31, 2959): 39.24471733757997, (31, 2960): 39.768637591361596, (31, 2961): 39.886665357327296, (31, 2963): 40.00836133643999, (31, 2968): 40.43541543685951, (31, 2976): 39.62222280287357, (31, 2981): 41.75669076609135, (31, 2982): 42.42106573206475, (31, 2984): 42.49896138366351, (31, 3003): 43.14267415459967, (31, 3046): 33.922608903777196, (31, 3050): 38.61166720602465, (31, 3051): 38.40489768355803, (31, 3053): 38.524495757666315, (31, 3069): 40.79634748028609, (31, 3071): 36.841717817151526, (31, 3080): 51.846261161768325, (31, 3199): 47.260711122359744, (31, 3200): 47.59398575004528, (31, 3205): 48.21126401790089, (31, 3209): 47.75197645814844, (31, 3215): 47.20766475371796, (31, 3217): 47.14183029674462, (31, 3249): 46.79843794785942, (31, 3263): 47.46879949940115, (31, 3289): 45.88794612567381, (31, 3301): 46.93515613181348, (31, 3302): 46.52271381516983, (31, 3307): 46.3714261836107, (31, 3310): 46.9803887309343, (31, 3391): 66.58541149908545, (31, 3509): 108.81949007710779, (31, 3510): 109.30485342259242, (31, 3511): 108.8743985359729, (31, 3512): 109.0834054993123, (31, 3514): 108.89923064186077, (31, 3519): 108.2452142123607, (31, 3536): 107.7735551820426, (31, 3545): 106.90315024572867, (31, 3548): 107.5155811275745, (31, 3572): 107.62842156717392, (31, 3581): 108.58813726706828, (31, 3583): 108.46355795646762, (31, 3601): 107.53382377759002, (31, 3656): 108.79704994075355, (31, 3669): 110.8569592319491, (31, 3670): 110.48830656511458, (31, 3695): 112.41196213742799, (31, 3696): 112.05757896017107, (31, 3782): 105.8966699947141, (31, 3792): 106.6223655029851, (31, 3989): 324.2831302871547, (31, 4008): 326.9528871088467, (31, 4031): 326.5915549807367, (31, 4045): 325.82350302172887, (31, 4144): 326.13759852409316, (31, 4145): 323.62691133199144, (31, 4164): 325.1471893942229, (31, 4168): 324.39441261993403, (31, 4173): 324.26379908937656, (31, 4181): 322.63134895696146, (31, 4228): 320.90727406167264, (31, 4248): 320.47884984521176, (31, 4254): 306.30911277923565, (31, 4260): 306.32090597410087, (31, 4262): 307.30285921968715, (31, 4273): 307.0672926440364, (31, 4319): 298.1584249588639, (31, 4326): 297.85336243557236, (31, 4328): 297.9680956810844, (31, 4334): 298.54849947666645, (31, 4335): 298.33210453890274, (31, 4372): 277.73750249495527, (31, 4413): 284.82304122119143, (31, 4434): 277.6035881651315, (31, 4447): 279.2010193103971, (31, 4452): 277.6202999204805, (31, 4463): 257.91271795445067, (31, 4465): 258.6931569668292, (31, 4619): 283.81384609363573, (31, 4645): 286.0187055697641, (31, 4657): 285.4710670317536, (31, 4666): 284.5098454666852, (31, 4676): 285.8455745779055, (31, 4678): 286.26141276906355, (31, 4689): 285.0552357518225, (31, 4704): 291.64578562913835, (31, 4726): 302.00751521496215, (31, 4727): 301.79147858287246, (31, 4730): 301.3920339060091, (31, 4731): 301.37828918875874, (31, 4734): 302.3475143755661, (31, 4735): 302.0324379435082, (31, 4736): 302.04005368163837, (31, 4737): 301.5463243586596, (31, 4738): 301.517419570533, (31, 4756): 301.6746900094345, (31, 4760): 301.12991546301737, (31, 4761): 301.46886987901945, (31, 4762): 300.7027714744223, (31, 4765): 301.17160142400377, (31, 4773): 302.5405918604898, (31, 4774): 302.1619644316662, (31, 4790): 302.4246979770362, (31, 4795): 302.28226955562144, (31, 4799): 302.1570786938654, (31, 4801): 302.3556285171104, (31, 4804): 302.58782828109827, (31, 4805): 302.4679757222181, (31, 4806): 301.80592866048477, (31, 4815): 301.4352228692436, (31, 4816): 302.06138498275243, (31, 4817): 301.9543158852072, (31, 4826): 301.6976433056578, (31, 4830): 301.29912003804895, (31, 4839): 301.7494593775859, (31, 4840): 301.85139183952464, (31, 4841): 301.3214455876165, (31, 4846): 301.20743333411156, (31, 4848): 300.97479413435246, (31, 4850): 301.140038636641, (31, 4871): 299.4690810097532, (31, 4883): 301.1528306819485, (31, 4900): 300.543322575857, (31, 4901): 300.128552851288, (31, 4917): 280.16299864928294, (31, 4931): 278.3761959146677, (31, 4944): 280.5036341354646, (31, 4956): 278.5659829483677, (31, 4958): 278.24152053287025, (31, 4959): 277.71535302256376, (31, 4961): 279.0391197815963, (31, 4966): 277.9713440028225, (31, 5207): 275.9645835060666, (31, 5272): 250.93685571093042, (31, 5283): 251.48541508321145, (31, 5287): 251.743923145697, (31, 5289): 251.9617903133037, (31, 5293): 251.64182525577917, (31, 5295): 253.26670108885952, (31, 5296): 252.87915454512378, (31, 5298): 252.64995025092253, (31, 5303): 252.80807116821762, (31, 5305): 249.86911602785443, (31, 5306): 248.88318561013915, (31, 5307): 249.53763744819105, (31, 5308): 250.01096232501732, (31, 5313): 250.46374048014584, (31, 5314): 250.97046145105853, (31, 5317): 249.76725568250887, (31, 5319): 252.1570166011404, (31, 5324): 252.1176187771054, (31, 5326): 252.11429318971628, (31, 5348): 248.42229937827656, (31, 5351): 248.3158237068302, (31, 5399): 251.73755844638768, (31, 5413): 248.20855350777228, (31, 5422): 252.4280111281234, (31, 5445): 250.92741327681802, (31, 5448): 250.36641698096017, (31, 5456): 249.83297909539706, (31, 5467): 250.2474662538433, (31, 5624): 245.39401718510717, (31, 5671): 268.70498120305655, (31, 5672): 267.97411199504734, (31, 5797): 277.7472125997644, (31, 5871): 256.1253198986565, (31, 5976): 249.248677612284, (31, 6118): 80.2855318084301, (31, 6248): 87.30585224993524, (31, 6345): 224.38250092941735, (31, 6352): 222.24864309302595, (31, 6354): 224.84388926870713, (31, 6359): 225.37475353986633, (31, 6376): 222.86207599063692, (31, 6378): 224.60280727827268, (31, 6381): 225.27606087637562, (31, 6383): 223.8854860422383, (31, 6396): 225.47765317823863, (31, 6399): 224.54233206172594, (31, 6408): 222.21407843363562, (31, 6409): 222.9320535443531, (31, 6419): 219.02651380431848, (31, 6422): 222.26618546715568, (31, 6423): 222.0774614681651, (31, 6424): 224.31676785519713, (31, 6439): 223.81553418925574, (31, 6464): 223.13425602747012, (31, 6465): 223.01489845782788, (31, 6469): 223.48649747454425, (31, 6470): 223.402899503757, (31, 6472): 226.1417492347404, (31, 6480): 225.23303623463104, (31, 6486): 226.05546283162334, (31, 6497): 225.75324089585206, (31, 6503): 222.74969136320271, (31, 6508): 223.18171165591505, (31, 6509): 223.47212668326043, (31, 6521): 225.30312694564435, (31, 6544): 224.88768425578075, (31, 6552): 222.14675452620736, (31, 6553): 221.7826388199495, (31, 6554): 221.41584364459453, (31, 6578): 222.7952386758015, (31, 6582): 222.24907016513822, (31, 6601): 222.90087184105997, (31, 6609): 226.0635457956204, (31, 6610): 226.10455304443278, (31, 6611): 226.3308462246979, (31, 6614): 226.24045681684993, (31, 6615): 226.2507369246833, (31, 6616): 226.41800648439033, (31, 6617): 226.3265610381865, (31, 6618): 226.6474851187886, (31, 6619): 225.95098310938863, (31, 6620): 226.33016940510907, (31, 6621): 226.00866359477052, (31, 6622): 226.14535963155325, (31, 6623): 226.10114587589138, (31, 6624): 225.73059690673216, (31, 6625): 225.72621912857846, (31, 6626): 225.9771655259266, (31, 6627): 226.2526822097774, (31, 6628): 226.17114347200868, (31, 6629): 225.69637465437592, (31, 6630): 225.62373816312538, (31, 6632): 225.718670494429, (31, 6634): 225.23457334645386, (31, 6635): 225.95155050153392, (31, 6636): 226.40182018217837, (31, 6637): 225.27085520416648, (31, 6638): 225.56703483689765, (31, 6639): 226.22608273991403, (31, 6640): 225.66743416278237, (31, 6641): 225.92678655251743, (31, 6642): 225.509056099233, (31, 6643): 226.01351652383786, (31, 6645): 225.94861847310804, (31, 6646): 226.6135383569585, (31, 6647): 225.63609564850256, (31, 6653): 226.2672969576016, (31, 6655): 226.26166307994566, (31, 6658): 225.1737962926977, (31, 6662): 225.4222685293949, (31, 6819): 206.86041112188556, (31, 6996): 211.56427736349798, (31, 7059): 215.71513991283564, (31, 7187): 206.77759718525863, (31, 7304): 198.85370184960004, (31, 7528): 210.3033830855848, (31, 7720): 235.6925232487299, (31, 7793): 234.88905373258947, (31, 7807): 235.32187658051518, (31, 7808): 234.70120838072637, (31, 7831): 227.63916564771685, (31, 7850): 231.98006843721805, (31, 7852): 231.21429643713222, (31, 8012): 234.97652400765725, (31, 8125): 236.60632580030037, (31, 8208): 243.26718816182154, (31, 8392): 229.40836534597778, (31, 8651): 187.04077937573487, (31, 9088): 207.4528510426925, (31, 9443): 173.6903166926612, (31, 9444): 174.25386650665087, (31, 9828): 154.50779189710892, (31, 9868): 154.67529564042226, (31, 10180): 236.90732056509825, (31, 10256): 247.512820562404, (31, 10276): 242.81012349225236, (31, 10378): 244.8262482652046, (31, 10676): 232.4713694621212, (31, 10714): 225.232446716034, (31, 10730): 227.12926061113643, (31, 10862): 215.37728916941538, (31, 10881): 217.01899426760588, (31, 10883): 216.75915970953176, (31, 10885): 215.04419977839902, (31, 10891): 216.35600795544443, (31, 10909): 216.39698375960967, (31, 10911): 216.81780825847173, (31, 10913): 216.3773901345591, (31, 10915): 216.4587035066482, (31, 10919): 216.7697078875122, (31, 11037): 203.43645483244563, (31, 11039): 200.13126110415988, (31, 11516): 350.3248530143608, (31, 11856): 298.8100432859566, (31, 11857): 298.34723856434726, (31, 11861): 298.5923029920103, (31, 11881): 298.21593997147534, (31, 11902): 296.3496709162425, (31, 11911): 296.0717493100981, (31, 11914): 296.30508163423804, (31, 11922): 297.67099403501476, (31, 11924): 298.1263521216028, (31, 11926): 297.59232140397967, (31, 11950): 298.71709209879094, (31, 11963): 300.46422745627086, (31, 11983): 299.3608016301368, (31, 11985): 301.33586259273005, (31, 12009): 301.0662870806819, (31, 12010): 299.80896853050393, (31, 12018): 300.0228323967276, (31, 12020): 300.3494922336128, (31, 12021): 300.5627073706589, (31, 12024): 301.7486316326213, (31, 12025): 301.333334448302, (31, 12027): 301.0561269647829, (31, 12031): 299.60100605419234, (31, 12032): 300.002429868988, (31, 12035): 301.00296691307386, (31, 12041): 301.43991510640933, (31, 12045): 285.0239325562836, (31, 12145): 292.70066507141723, (31, 12275): 325.10656029930357, (31, 12294): 321.89306798749703, (31, 12358): 331.7542407468795, (31, 12463): 335.56513260601395, (31, 12465): 335.45016782322415, (31, 12482): 337.1371221115969, (31, 12503): 336.90204041400705, (31, 12506): 337.3587368792373, (31, 12549): 336.37415702041324, (31, 12559): 336.0255390064696, (31, 12569): 336.3985803543482, (31, 12572): 336.74198816382244, (31, 12574): 336.024768607502, (31, 12576): 336.7709742193137, (31, 12591): 336.68804485561606, (31, 12608): 339.45625103899954, (31, 12696): 335.0154343696791, (31, 12710): 337.6022713097438, (31, 12728): 336.3454307758313, (31, 12766): 261.44810757036197, (31, 12771): 257.9482086187944, (31, 12790): 257.49421252379057, (31, 12795): 256.4631916411843, (31, 12797): 252.0041153435932, (31, 12798): 252.6038821625336, (31, 12811): 256.1182245412716, (31, 12830): 254.95840997863434, (31, 12848): 255.53513944198752, (31, 12850): 255.8098391470595, (31, 12852): 254.78043339530885, (31, 12854): 254.24160933415726, (31, 12859): 256.0618462445461, (31, 12861): 253.19220974267833, (31, 12865): 256.7956153773148, (31, 12866): 256.5076050364229, (31, 12867): 257.59642710903034, (31, 12874): 257.06979980495834, (31, 12875): 257.47275901489525, (31, 12881): 255.81384204711784, (31, 12883): 256.4787942544561, (31, 12885): 257.8289705945433, (31, 12888): 256.1627387824226, (31, 12889): 256.0051164891147, (31, 12892): 257.1895857592543, (31, 12893): 256.1948173178673, (31, 12896): 256.5081341706594, (31, 12906): 257.14095526369334, (31, 13018): 252.5998539510859, (31, 13071): 252.7360065429264, (31, 13131): 248.130833036222, (31, 13146): 251.607714812477, (31, 13159): 247.15740456493657, (31, 13193): 247.4218117007262, (31, 13198): 241.08635779991016, (31, 13292): 248.18116836364385, (31, 13296): 250.09115926486137, (31, 13406): 237.4831501601117, (31, 13407): 237.3042781441188, (31, 13417): 237.04040696569606, (31, 13418): 237.74296262435794, (31, 13438): 240.29101596359163, (31, 13442): 240.7636988036272, (31, 13443): 240.25074975835278, (31, 13764): 198.34290624792877, (31, 13766): 198.98575332082925, (31, 13771): 198.58678506330847, (31, 13783): 197.43226906321198, (31, 13784): 199.5902859615834, (31, 13792): 197.70327091073966, (31, 13824): 197.03450591254943, (31, 14017): 199.63969430098953, (31, 14870): 219.342142411311, (31, 14997): 203.58134411859885, (31, 15000): 203.66382832783836, (31, 15003): 204.13392600076773, (31, 15006): 205.07784240872567, (31, 15007): 205.534672259341, (31, 15056): 205.51889749426846, (31, 15063): 205.12182028312444, (31, 15069): 204.99189977209787, (31, 15076): 205.61523669321025, (31, 15086): 204.17048494679, (31, 15087): 203.6934038498263, (31, 15111): 202.31516468267526, (31, 15116): 203.10708953913, (31, 15722): 191.0451461124811, (31, 15998): 183.4729462481543, (31, 16073): 124.81061273260059, (31, 16939): 30.00104488429479, (31, 16940): 30.54829348749528, (31, 16951): 30.415926543812756, (31, 16963): 30.238588298194905, (31, 16965): 29.375826583556105, (31, 16969): 29.858917409960032, (31, 16970): 29.82872287610429, (31, 16971): 30.587877094317225, (31, 16973): 30.82038096420662, (31, 16974): 29.208150600995985, (31, 16976): 29.658453386285295, (31, 16978): 30.153390388461865, (31, 16980): 29.232891519564856, (31, 16982): 29.41761841209535, (31, 17045): 50.71057380255363, (31, 17048): 50.72491845632867, (31, 17304): 316.7723519171968, (31, 17305): 316.25474883773023, (31, 17330): 316.7123032577264, (31, 17334): 315.87953229898665, (31, 17343): 317.37757852351496, (31, 17345): 315.7896317506041, (31, 17347): 316.6115144501857, (31, 17351): 314.6541246985958, (31, 17372): 315.75776905557115, (31, 17373): 317.3334312573917, (31, 17377): 317.43927766370666, (31, 17382): 316.40125930421067, (31, 17383): 316.6134870900327, (31, 17389): 315.9960787250885, (31, 17400): 317.06234552101176, (31, 17401): 317.0506375126743, (31, 17402): 317.1182506927758, (31, 17403): 317.217114124341, (31, 17440): 315.78815374798404, (31, 17455): 317.15678784409266, (31, 17491): 317.2105203188405, (31, 17507): 315.3752414749324, (31, 17509): 315.96797854101237, (31, 17590): 314.20201169599864, (31, 17615): 311.29737091160297, (31, 17642): 311.8590999396677, (31, 17643): 311.79170922011673, (31, 17668): 311.28381820196057, (31, 17721): 309.9947711031351, (31, 17754): 315.5067038739804, (31, 17769): 315.62205104337113, (31, 17776): 313.21910695335947, (31, 17804): 316.5749652713292, (31, 17809): 317.1589801634668, (31, 17824): 316.8069736511632, (31, 17837): 314.96910848513664, (31, 17838): 315.0018939918275, (31, 17862): 314.5529370506156, (31, 17866): 315.8097265489891, (31, 17872): 314.15304507153894, (31, 17873): 313.18590306714543, (31, 17881): 314.66513755552575, (31, 17947): 85.81983813018083, (31, 17951): 86.8236820010022, (31, 17953): 87.14965750819873, (31, 17954): 87.16767140391558, (31, 17959): 85.79300407646924, (31, 17963): 85.92682453759828, (31, 18000): 91.59275031765135, (31, 18001): 91.5205551160062, (31, 18111): 87.08484787834651, (31, 18148): 111.16793332900208, (31, 18166): 102.41637250909356, (31, 18189): 92.41898165939548, (31, 18239): 317.6518412846252, (31, 18240): 317.63501747791395, (31, 18245): 317.7013244933073, (31, 18247): 317.56301235881875, (31, 18251): 317.6870797767739, (31, 18256): 317.80996306676855, (31, 18258): 317.6576613652031, (31, 18259): 317.67866033344274, (31, 18260): 317.7279858997394, (31, 18262): 317.82914826497966, (31, 18263): 317.8427085031208, (31, 18264): 317.89242265097647, (31, 18266): 317.8635846911183, (31, 18267): 317.9135981653479, (31, 18268): 317.9343863593281, (31, 18269): 318.03292466229266, (31, 18275): 317.98639456465196, (31, 18285): 317.87947243080487, (31, 18308): 316.83748096917964, (31, 18313): 316.45635672561895, (31, 18314): 316.6003936540654, (31, 18315): 318.05601402012365, (31, 18316): 318.0338985950899, (31, 18317): 318.07913976809857, (31, 18320): 318.14150102691934, (31, 18321): 318.1602233882883, (31, 18322): 318.23428310903154, (31, 18324): 318.31412578155346, (31, 18325): 318.5634797178471, (31, 18326): 318.4712066169391, (31, 18327): 318.10907689102953, (31, 18329): 318.6906771252078, (31, 18330): 318.52348841569597, (31, 18331): 318.36338127515256, (31, 18332): 318.1913693638108, (31, 18333): 318.5097082410224, (31, 18336): 318.39018399792604, (31, 18337): 318.4835668416064, (31, 18403): 318.2800897477524, (31, 18432): 314.45578077706756, (31, 18451): 317.0502604944533, (31, 18466): 319.59159325160107, (31, 18481): 318.15627054480944, (31, 18483): 318.1469469262046, (31, 18484): 318.0167611180002, (31, 18485): 317.633627032381, (31, 18486): 318.0332160139141, (31, 18487): 317.72423516493825, (31, 18489): 317.96514070645844, (31, 18490): 318.30776043713036, (31, 18491): 318.45812872445947, (31, 18492): 317.39567031186175, (31, 18493): 317.99003048072257, (31, 18494): 317.89686883393784, (31, 18495): 318.19701259256493, (31, 18496): 318.0322560322661, (31, 18497): 317.66091494059714, (31, 18498): 317.6993895064479, (31, 18499): 317.9303339323067, (31, 18501): 317.77842444749604, (31, 18502): 317.631592595634, (31, 18503): 317.5085134794621, (31, 18504): 318.0837356455696, (31, 18506): 317.82490276691976, (31, 18507): 317.68956486223647, (31, 18508): 317.90656096550055, (31, 18509): 317.917665932999, (31, 18510): 317.52420031360015, (31, 18511): 318.0518812449813, (31, 18512): 317.86119425336767, (31, 18515): 318.11006139980367, (31, 18516): 318.14976910209447, (31, 18517): 317.97624951785406, (31, 18518): 318.26442751491464, (31, 18519): 318.1106665730815, (31, 18520): 317.8525503579607, (31, 18522): 318.7218721960499, (31, 18523): 318.76373538003094, (31, 18532): 318.9834690128447, (31, 18535): 318.53670227082, (31, 18537): 318.28793796424776, (31, 18539): 318.34488492778445, (31, 18540): 318.3790300759073, (31, 18541): 318.50574000999893, (31, 18542): 318.5852902413283, (31, 18543): 318.1938869615994, (31, 18546): 318.395568086267, (31, 18555): 318.7862726862504, (31, 18556): 318.8635634849248, (31, 18565): 318.9670012329985, (31, 18567): 319.0990252817996, (31, 18568): 318.8783814732372, (31, 18577): 320.40250563187135, (31, 18583): 320.1220235213594, (31, 18605): 320.4123828886709, (31, 18608): 319.2656128485571, (31, 18616): 321.83736298989874, (31, 18618): 323.0649557762775, (31, 18625): 322.58537606849006, (31, 18645): 321.4857162350043, (31, 18646): 321.78762802147924, (31, 18653): 320.83854535833103, (31, 18654): 321.8169787001728, (31, 18655): 321.18720587031726, (31, 18666): 325.0180724471179, (31, 18837): 319.49257955424923, (31, 18974): 316.7926957473321, (31, 18999): 317.68614226435744, (31, 19000): 318.0515336800638, (31, 19174): 300.0779112217171, (31, 19342): 307.3330933326736, (31, 19455): 303.21241815438725, (31, 19555): 285.0796974235452, (31, 19564): 286.1425306153217, (31, 19573): 285.3662895950508, (31, 19586): 285.02082108302994, (31, 19605): 285.3154355168082, (31, 19611): 285.84105875298275, (31, 19614): 285.60607832755557, (31, 19641): 294.4101965630352, (31, 19702): 294.24918853691605, (31, 19713): 293.6066952760902, (31, 19731): 282.0975237109568, (31, 19819): 300.428248420389, (31, 19893): 277.7717084151162, (31, 19899): 281.2776693000283, (31, 19929): 278.83145307300856, (31, 19951): 286.31445206843864, (31, 19962): 279.17809774727687, (31, 19970): 281.3613781796379, (31, 19971): 281.27209960520156, (31, 19972): 280.5496264581905, (31, 19975): 280.33914468680996, (31, 19978): 288.4840689506254, (31, 19987): 288.7005805998776, (31, 19989): 286.6258193365533, (31, 20039): 289.1247126664439, (31, 20043): 290.11326226974643, (31, 20047): 289.5552394442757, (31, 20052): 287.1601354813897, (31, 20054): 287.28428293533455, (31, 20085): 298.5356813777511, (31, 20104): 299.2171173075064, (31, 20132): 294.92331705019126, (31, 20203): 276.17664435585294, (31, 20280): 274.9256638472521, (31, 20285): 274.5404248041059, (31, 20290): 275.369072347833, (31, 20297): 274.6914412909233, (31, 20309): 288.0844922556085, (31, 20453): 299.8992424992954, (31, 20485): 270.3873317171976, (31, 20520): 268.6870222529865, (31, 20526): 267.59857990811264, (31, 20698): 185.25474568110968, (31, 20868): 165.01663536194636, (31, 21042): 255.37076084605818, (31, 21057): 260.1990021857887, (31, 21066): 257.777748741465, (31, 21075): 256.94908863692314, (31, 21093): 255.65786181309934, (31, 21098): 258.9741053440185, (31, 21127): 255.72750214148965, (31, 21130): 256.60094664239784, (31, 21144): 256.5360096208548, (31, 21146): 255.4124418424736, (31, 21147): 256.4769135396895, (31, 21148): 257.28918833352003, (31, 21153): 255.5738391383411, (31, 21293): 263.2651000540553, (31, 21426): 262.7028297768192, (31, 21442): 267.93025760478434, (31, 21451): 268.4310822931437, (31, 21466): 265.27139063320914, (31, 21469): 266.01634063886905, (31, 21471): 264.8949041666256, (31, 21473): 265.5034016108759, (31, 21475): 264.950989221525, (31, 21482): 266.5109033146382, (31, 21484): 266.34317133552065, (31, 21488): 265.91293543318574, (31, 21494): 264.912689316313, (31, 21498): 265.47652825532316, (31, 21500): 264.55739175948946, (31, 21514): 265.94505486813927, (31, 21537): 264.3205684554933, (31, 21662): 266.5285871828238, (31, 21691): 263.57298872656935, (31, 21757): 258.57364654930063, (31, 21777): 245.8129041160874, (31, 21778): 245.0672486345474, (31, 21779): 245.44216457438515, (31, 21790): 246.69732127505233, (31, 21802): 246.5766454477527, (31, 21824): 247.31037270977376, (31, 21874): 245.5844699945331, (31, 21879): 245.06826577022468, (31, 21983): 248.63201634637144, (31, 22002): 256.39225706824817, (31, 22132): 252.25501741787312, (31, 22261): 151.44396805817698, (31, 22298): 153.3353137616321, (31, 22339): 146.41361857618386, (31, 22508): 165.39650756433946, (31, 22841): 108.16302864338853, (31, 22842): 107.78645857800632, (31, 22874): 106.07818874633864, (31, 22941): 107.40490813630609, (31, 22956): 107.33035778189966, (31, 22960): 108.3121460086932, (31, 22968): 103.40047525386888, (31, 22970): 104.21995640996839, (31, 22974): 101.08877832170545, (31, 22980): 101.38589729288731, (31, 23025): 96.64370837172142, (31, 23028): 95.60105960507981, (31, 23081): 90.26300286416955, (31, 23104): 81.58029809258619, (31, 23147): 93.14969328569289, (31, 23298): 278.7202165928243, (31, 23376): 276.56972628860774, (31, 23381): 275.14595701240194, (31, 23529): 279.9828307379698, (31, 23556): 278.7565856622003, (31, 23718): 277.50847521988743, (31, 24001): 291.4659760231072, (31, 24094): 295.2456143610848, (31, 24129): 297.37670128740984, (31, 24174): 292.87615245733554, (31, 24235): 297.5621497103101, (31, 24259): 299.6447486792386, (31, 24260): 299.4851297645861, (31, 24261): 299.0348966489872, (31, 24305): 302.09312449322925, (31, 24306): 302.4956035461482, (31, 24307): 301.880667459272, (31, 24308): 296.86531320985097, (31, 24498): 307.57514376727994, (31, 24499): 307.61933968023925, (31, 24500): 307.2288644134009, (31, 24668): 304.67079308841795, (31, 24711): 310.1899447288936, (31, 24756): 311.60191107692805, (31, 24788): 312.2141420632789, (31, 24809): 309.84658418291576, (31, 24813): 310.585017337844, (31, 24821): 310.34184022833705, (31, 24825): 310.52497511780865, (31, 24832): 309.6838074893982, (31, 24833): 310.0469103724228, (31, 24835): 310.4095170819662, (31, 24837): 310.9847690475357, (31, 24840): 309.6288050890573, (31, 24841): 310.18726412848554, (31, 24844): 309.6470067456043, (31, 24845): 309.9710503688471, (31, 24846): 309.94902732739934, (31, 24849): 310.1477521211066, (31, 24850): 310.6980786877273, (31, 24863): 305.63497253714286, (31, 24866): 306.28350608822234, (31, 24885): 307.05901241760444, (31, 24886): 307.11916059750087, (31, 24889): 308.5252818270034, (31, 24903): 309.0668621272234, (31, 24909): 306.6893502824702, (31, 24999): 334.4532923680042, (31, 25019): 333.6520752743103, (31, 25028): 334.0888083699885, (31, 25137): 274.8064133851925, (31, 25145): 275.64919163661875, (31, 25208): 283.9494190941636, (31, 25233): 282.76563047874583, (31, 25371): 275.7577779009331, (31, 25377): 273.640306013307, (31, 25828): 231.76437171899525, (31, 25851): 225.90469084355462, (31, 25874): 231.7904661745266, (31, 25898): 234.04195728826684, (31, 25946): 231.14364356369734, (31, 26047): 243.5630979976049, (31, 26066): 260.78574772824476, (31, 26197): 250.04828683127997, (31, 26212): 209.82858632315558, (31, 26253): 207.64411281755145, (31, 26254): 208.47428299261216, (31, 26257): 209.24587224325305, (31, 26258): 208.08533493202648, (31, 26260): 208.68142096144766, (31, 26266): 207.83040892251316, (31, 26267): 208.53900042995835, (31, 26271): 208.56522884316155, (31, 26304): 216.28537625599023, (31, 26305): 216.2184049799135, (31, 26363): 229.13752042872426, (31, 26441): 159.64143126096923, (31, 26442): 159.61284112960232, (31, 26450): 160.64816864754943, (31, 26459): 161.68935212569937, (31, 26462): 161.97641508748882, (31, 26467): 159.15260616772238, (31, 26471): 159.44227511556838, (31, 26472): 159.3810293870891, (31, 26473): 159.27350427521426, (31, 26476): 158.3067389410532, (31, 26485): 160.72357863416562, (31, 26493): 160.19863715233183, (31, 26524): 161.98935467396285, (31, 26525): 161.83141916937396, (31, 26556): 159.87296902654498, (31, 26560): 160.79066245702128, (31, 26561): 161.59138503790686, (31, 26564): 159.91170636279446, (31, 26569): 161.46751803012887, (31, 26570): 161.39794458686083, (31, 26573): 160.80556676764508, (31, 26581): 160.44166279072022, (31, 26583): 160.89373946060223, (31, 26593): 159.94886662154545, (31, 26837): 158.55850302691613, (31, 26844): 158.1011198064963, (31, 26863): 158.1501457050087, (31, 26893): 156.41195898137892, (31, 26902): 155.74945635962382, (31, 26905): 157.28452520111654, (31, 26912): 156.4961907997153, (31, 26921): 157.37470583814348, (31, 26922): 157.41078895409697, (31, 27212): 177.69166492408363, (31, 27218): 179.21035123901652, (31, 27239): 176.71779653254848, (31, 27257): 176.7381029135055, (31, 27274): 176.35589226284893, (31, 27279): 176.02943164052326, (31, 27282): 176.4979570184545, (31, 27283): 177.1036789442504, (31, 27285): 175.90082510495617, (31, 27286): 175.6172094205131, (31, 27290): 176.83450615994815, (31, 27295): 177.72792586730006, (31, 27300): 176.4375502223187, (31, 27344): 175.87159310426523, (31, 27366): 174.935422488909, (31, 27383): 175.00345897399583, (31, 27398): 175.43841408631818, (31, 27406): 176.19557165403427, (31, 27407): 176.38951160247606, (31, 27426): 179.77856020280203, (31, 27432): 180.89237053916818, (31, 27460): 180.5611525222145, (31, 27523): 168.58822394589257, (31, 27545): 167.6728524890432, (31, 27602): 155.3714735584885, (31, 27606): 155.79203833228038, (31, 27646): 157.91135112150846, (31, 27667): 155.37439935628197, (31, 27672): 155.5658577995696, (31, 27674): 155.79316007899303, (31, 27688): 156.71108169536677, (31, 27692): 154.76253445220092, (31, 27693): 155.07034454804975, (31, 27705): 154.7232965181839, (31, 27712): 154.261221079845, (31, 27786): 169.65549751830042, (31, 27790): 175.59207157087303, (31, 27791): 176.3969993885688, (31, 27795): 169.64928614975426, (31, 27801): 173.60493198074457, (31, 27813): 168.83461006041094, (31, 27816): 170.13192087744872, (31, 27823): 173.79998959922364, (31, 27830): 171.64093705283543, (31, 27884): 158.7542308090438, (31, 27885): 158.43660776153757, (31, 27896): 158.77592480501244, (31, 27919): 159.13200275173793, (31, 27922): 158.5958916694109, (31, 27930): 159.1101503165468, (31, 27934): 158.7996945281179, (31, 27935): 158.4508860792906, (31, 27948): 138.47739412715143, (31, 27951): 143.60866563067182, (31, 28061): 121.06616175389574, (31, 28290): 91.93753950881029, (31, 28292): 90.08673150997008, (31, 28293): 91.47170986383631, (31, 28295): 90.8792652432345, (31, 28296): 91.52045790017863, (31, 28297): 92.83196199037766, (31, 28302): 92.27288959083883, (31, 28310): 76.56216175578919, (31, 28313): 77.75852217629648, (31, 28372): 74.46186218095421, (31, 28398): 74.64351007885817, (31, 28399): 75.05949163981106, (31, 28400): 74.79630720022993, (31, 28401): 75.10292568854706, (31, 28445): 79.05723769813073, (31, 28475): 73.57094676565406, (31, 28885): 296.6853693761952, (31, 28886): 296.23676275238233, (31, 28915): 296.4007933785429, (31, 28916): 296.11880870376706, (31, 28917): 295.8601298431246, (31, 28921): 297.47532706608723, (31, 28931): 297.3178458422529, (31, 28945): 294.6912915799482, (31, 28982): 295.3910693820891, (31, 29219): 296.63279620029164, (31, 29228): 294.8807498861662, (31, 29246): 305.6940126159255, (31, 29248): 305.3219696096057, (31, 29282): 303.03363908680615, (31, 29290): 307.05812433417924, (31, 29291): 306.53113783017346, (31, 29292): 306.99451073192444, (31, 29293): 306.08837984532306, (31, 29294): 306.719873018616, (31, 29298): 306.1014318471237, (31, 29299): 305.96729345290805, (31, 29304): 305.24528617950233, (31, 29317): 303.1431932679137, (31, 29323): 302.986188349956, (31, 29330): 303.9894731630254, (31, 29331): 304.53435343689557, (31, 29344): 296.4133029796241, (31, 29445): 275.4033143662488, (31, 29724): 122.62667698898527, (31, 29738): 122.66854649435895, (31, 29745): 123.115356507217, (31, 29748): 126.00742449943932, (31, 29750): 127.28357170984208, (31, 29759): 125.59911695981663, (31, 29772): 125.80205517757221, (31, 29781): 125.83909063514531, (31, 29784): 124.57382803264412, (31, 29790): 126.38892467913166, (31, 29811): 127.54078095286694, (31, 29817): 135.379033730141, (31, 29818): 135.45720208684943, (31, 29929): 121.30907642753861, (31, 30039): 113.86554034061173, (31, 30066): 108.82069829601681, (31, 30116): 114.17436436149106, (31, 30238): 123.09185556334627, (31, 30248): 110.49843640479233, (31, 30260): 109.68831747095788, (31, 30545): 291.0855183085718, (31, 30733): 272.16543195967563, (31, 30756): 266.43216410942466, (31, 30921): 275.9639460497907, (31, 31079): 228.64365179786964, (31, 31149): 226.1017796834114, (31, 31154): 226.14455806455143, (31, 31160): 225.95362903462222, (31, 31163): 225.83932065002875, (31, 31189): 217.81790882542543, (31, 31215): 218.28076589098748, (31, 31259): 217.2365706124274, (31, 31262): 216.37321127973533, (31, 31430): 229.43606245418582, (31, 31568): 206.8308637429999, (31, 31751): 224.2641988641624, (32, 109): 27.053322045089786, (32, 872): 163.71375386692853, (32, 873): 164.64973564639695, (32, 877): 164.40054699697032, (32, 879): 164.54933393672744, (32, 884): 163.8386060285944, (32, 889): 164.3762240018542, (32, 891): 163.50131135147765, (32, 892): 165.25374348286476, (32, 894): 165.0938204915051, (32, 896): 164.02324013509164, (32, 903): 164.55257561948463, (32, 909): 162.6245279992402, (32, 910): 162.90541653463686, (32, 912): 162.30852768092186, (32, 913): 161.68545446362995, (32, 916): 161.28459610871582, (32, 926): 163.0895300557774, (32, 927): 162.7545025226116, (32, 948): 163.14550789658023, (32, 961): 163.2750193165392, (32, 962): 163.31572402462092, (32, 963): 163.38271944395845, (32, 967): 164.90665225685052, (32, 974): 164.6445686071706, (32, 998): 165.36131195513573, (32, 1014): 184.6070639665756, (32, 1086): 158.78962240320135, (32, 1087): 158.36506942111717, (32, 1089): 157.6650123587233, (32, 1090): 158.08328673542252, (32, 1092): 159.42810173308206, (32, 1097): 158.46311123819254, (32, 1107): 159.90386567392417, (32, 1387): 17.951322441289292, (32, 1554): 12.5, (32, 1827): 208.59627165759912, (32, 1828): 208.64926945804513, (32, 1829): 208.8245466364576, (32, 1830): 208.89496936633194, (32, 1831): 208.93992259563893, (32, 1832): 208.8179206827668, (32, 1833): 208.79166314344565, (32, 1836): 208.64142008145186, (32, 1841): 209.29688486610019, (32, 1843): 209.045372258267, (32, 1844): 209.19461589282892, (32, 1845): 208.92794959868291, (32, 1847): 207.84837773633586, (32, 1848): 208.19571618456118, (32, 1849): 209.86070540316712, (32, 1850): 209.99649090487193, (32, 1851): 208.56147383829094, (32, 1852): 208.6734940961767, (32, 1854): 208.77112189183018, (32, 1856): 207.91380819519304, (32, 1857): 208.21932890201884, (32, 1858): 209.64241814474371, (32, 1861): 208.87719848893337, (32, 1866): 207.9668509578723, (32, 1867): 209.24118466009872, (32, 1868): 208.96856040972375, (32, 1870): 209.2787689150109, (32, 1871): 209.12278769775617, (32, 1875): 208.69498449678903, (32, 1880): 208.05229676021477, (32, 1882): 208.27806056179884, (32, 1883): 209.911269202554, (32, 1889): 208.08672910225488, (32, 1893): 208.70197501114194, (32, 1894): 208.43885198231447, (32, 1899): 207.8171486167393, (32, 1900): 207.96345319698437, (32, 1902): 209.11583979405904, (32, 1905): 209.47993598027637, (32, 1907): 208.33825211947948, (32, 1910): 208.3449078442761, (32, 1917): 209.84640996099873, (32, 1920): 208.285107603661, (32, 1935): 209.3562597761893, (32, 1937): 209.64658631444848, (32, 1946): 207.0922518400876, (32, 1949): 207.3386119636201, (32, 1950): 206.5374549078868, (32, 1951): 206.97156446424438, (32, 1952): 207.56363143171595, (32, 1953): 207.5159168248221, (32, 1954): 207.43635440947057, (32, 1958): 207.34941893214824, (32, 1960): 207.89722813422696, (32, 1968): 208.1128989046458, (32, 1969): 209.249085339323, (32, 1974): 208.9668703395054, (32, 1975): 209.01933626232963, (32, 1979): 208.21714816276986, (32, 1980): 208.3316696826275, (32, 1981): 208.42729935497, (32, 1985): 208.54670099860326, (32, 1994): 206.5364162948435, (32, 2011): 208.3240784108395, (32, 2019): 210.9880646394237, (32, 2020): 210.63707893460702, (32, 2029): 209.47182418182592, (32, 2030): 210.39110752331234, (32, 2032): 209.36813348401762, (32, 2033): 209.90220690926492, (32, 2034): 209.97607489036074, (32, 2036): 209.1360006049845, (32, 2037): 209.3370086177198, (32, 2038): 209.04112531283192, (32, 2042): 212.81673294740696, (32, 2050): 209.60907890107006, (32, 2051): 209.6458563427864, (32, 2053): 209.70597270391457, (32, 2054): 210.0431258962458, (32, 2066): 209.3730802028501, (32, 2067): 209.32853103465044, (32, 2071): 205.8624352096711, (32, 2072): 206.41537980788962, (32, 2073): 204.48082651490654, (32, 2074): 204.45451183215687, (32, 2080): 203.55431259815975, (32, 2082): 206.7340026522943, (32, 2083): 207.01449720348077, (32, 2089): 206.27384950111406, (32, 2090): 206.5201496421169, (32, 2092): 206.0646846389027, (32, 2098): 203.83658729761822, (32, 2099): 204.24896536066797, (32, 2101): 203.85178502030874, (32, 2102): 205.42428765916955, (32, 2103): 204.96240431782144, (32, 2104): 204.7478258673363, (32, 2106): 207.2645870806945, (32, 2112): 204.13577250809945, (32, 2113): 205.69754253569388, (32, 2114): 206.21578262226748, (32, 2117): 207.5723102493223, (32, 2123): 202.13092721208804, (32, 2124): 202.4563239692256, (32, 2134): 201.732419681404, (32, 2138): 202.60822585371798, (32, 2141): 201.7825003966012, (32, 2148): 203.05436755889306, (32, 2150): 201.02857895637882, (32, 2151): 201.42897417802655, (32, 2152): 200.9026567855885, (32, 2153): 203.08757550293018, (32, 2154): 201.690388400691, (32, 2155): 201.6713466753886, (32, 2156): 201.32337711359162, (32, 2157): 202.16387018503625, (32, 2160): 203.44402185247176, (32, 2161): 200.92527019974463, (32, 2162): 203.44944769222099, (32, 2163): 202.9657134990833, (32, 2164): 202.9842861254438, (32, 2168): 201.56795268265873, (32, 2172): 202.23955485846088, (32, 2174): 201.4893913339352, (32, 2178): 202.61481079456513, (32, 2179): 202.43517518584156, (32, 2183): 202.6772456000881, (32, 2185): 202.74659391716656, (32, 2186): 202.46096181751494, (32, 2190): 203.42099653560874, (32, 2192): 202.92355664233875, (32, 2193): 202.74117678626138, (32, 2194): 202.23342312418634, (32, 2195): 202.26478922838814, (32, 2197): 203.08395518319938, (32, 2205): 202.52258492277986, (32, 2207): 201.7595750886574, (32, 2208): 202.2073630037365, (32, 2212): 202.66075224182012, (32, 2214): 194.33243055809692, (32, 2225): 195.82919056656624, (32, 2231): 191.21628778943585, (32, 2278): 201.47733954348186, (32, 2284): 202.68039448354764, (32, 2285): 202.61037574241323, (32, 2291): 201.06784785158203, (32, 2292): 200.6999158323025, (32, 2307): 202.02931388443142, (32, 2313): 201.0129543505856, (32, 2317): 199.7069381431985, (32, 2319): 201.11015839344765, (32, 2321): 201.67763603361448, (32, 2323): 201.45074187518543, (32, 2326): 202.93988138783024, (32, 2327): 202.4949161150502, (32, 2329): 202.2080539065824, (32, 2330): 201.9198369959971, (32, 2332): 202.72956119713078, (32, 2344): 201.36001263515377, (32, 2346): 201.4531724328894, (32, 2361): 200.33743592382623, (32, 2368): 206.06992229977146, (32, 2374): 206.6473212839621, (32, 2375): 206.75522719573803, (32, 2377): 204.957135638452, (32, 2378): 207.1129625385199, (32, 2379): 207.26962592438383, (32, 2380): 207.35893405677106, (32, 2383): 205.34674985282538, (32, 2385): 205.57277753705273, (32, 2395): 205.50247278204537, (32, 2397): 207.11641472354316, (32, 2398): 204.39679643006093, (32, 2399): 204.9648483462733, (32, 2400): 204.8233958255549, (32, 2402): 206.12444406382994, (32, 2403): 206.51809650931156, (32, 2404): 206.57312469606828, (32, 2405): 205.66616697988962, (32, 2407): 206.33784783273518, (32, 2408): 206.84778133149487, (32, 2409): 205.92358172083462, (32, 2411): 206.7038061239167, (32, 2412): 206.52972740760185, (32, 2413): 206.87853614829226, (32, 2414): 206.37925555178066, (32, 2422): 206.64992134604398, (32, 2424): 206.59945624226907, (32, 2426): 206.64637679655434, (32, 2433): 205.98811592247893, (32, 2436): 205.91715787687676, (32, 2437): 203.59184563649447, (32, 2440): 204.07057814773472, (32, 2445): 215.21620760399384, (32, 2447): 213.864593337592, (32, 2454): 215.03149781554148, (32, 2455): 215.00543300706474, (32, 2460): 211.5033175776328, (32, 2461): 211.95547472115894, (32, 2471): 219.68055621380984, (32, 2492): 215.7185946317548, (32, 2511): 211.50199177001156, (32, 2523): 213.6717794794186, (32, 2525): 213.3355050692354, (32, 2535): 212.30527067045432, (32, 2537): 211.57328469354687, (32, 2538): 211.98582377770344, (32, 2539): 212.2133925214596, (32, 2540): 212.64903430014672, (32, 2542): 213.33878115564485, (32, 2559): 223.4962307902088, (32, 2575): 223.02634462518787, (32, 2599): 204.97899496807793, (32, 2600): 209.0369089356344, (32, 2607): 206.35041448659902, (32, 2627): 215.37666380588243, (32, 2647): 217.7846837825448, (32, 2674): 216.197726263203, (32, 2681): 216.15840266857813, (32, 2683): 217.06205156808704, (32, 2686): 215.77350452019988, (32, 2689): 229.5682764240274, (32, 2690): 229.6942923309495, (32, 2713): 234.13886377365523, (32, 2714): 234.61851965356541, (32, 2715): 234.93942438056823, (32, 2739): 234.58053999668178, (32, 2740): 231.85513970621162, (32, 2741): 231.96569567355576, (32, 2749): 234.402617652206, (32, 2750): 234.41352110739672, (32, 2752): 234.6019625177053, (32, 2755): 234.91277977242785, (32, 2758): 234.9139216938999, (32, 2759): 234.8747346365986, (32, 2769): 234.39889966647965, (32, 2771): 232.5565097074199, (32, 2779): 233.30789429774492, (32, 2784): 229.9542257413846, (32, 2800): 231.25646920800833, (32, 2802): 231.57612206308855, (32, 2803): 231.37159868966066, (32, 2804): 231.1230544467639, (32, 2805): 232.09516397622102, (32, 2807): 231.99222559249426, (32, 2809): 232.05646495281826, (32, 2812): 229.76791072077404, (32, 2814): 232.4971967189854, (32, 2817): 233.3171763950861, (32, 2819): 231.83236092467743, (32, 2823): 230.68839072099615, (32, 2832): 232.614928726865, (32, 2836): 231.1434646124858, (32, 2839): 231.9037394198843, (32, 2841): 233.00919250829486, (32, 2843): 232.76641150709986, (32, 2846): 231.76879124067324, (32, 2849): 232.98420887247724, (32, 2852): 232.5970839090794, (32, 2853): 233.16750526974718, (32, 2876): 233.7030801813564, (32, 2877): 234.94006469546983, (32, 2885): 236.08868368157698, (32, 2918): 231.47323277671546, (32, 2921): 232.0804010612452, (32, 2925): 228.96680408793145, (32, 2926): 227.77698305087094, (32, 2930): 230.8869258689609, (32, 2931): 229.4125457407527, (32, 2938): 231.62254401086682, (32, 2940): 232.433969374518, (32, 2947): 230.51172475925256, (32, 2949): 230.5479833637612, (32, 2950): 230.91807312209573, (32, 2952): 230.67008809335752, (32, 2958): 230.5629626747811, (32, 2959): 230.64327428064215, (32, 2960): 231.25947817185354, (32, 2961): 231.05412789034403, (32, 2963): 230.43096942282116, (32, 2968): 230.675242379547, (32, 2976): 230.27836820049603, (32, 2981): 226.5272456083284, (32, 2982): 226.56180560589206, (32, 2984): 226.35473993041654, (32, 3003): 226.1120246370396, (32, 3046): 220.9356712374818, (32, 3050): 224.3927709110764, (32, 3051): 224.52313190055114, (32, 3053): 224.05025079914623, (32, 3069): 227.3745151880152, (32, 3071): 223.53051770365133, (32, 3080): 236.3833774392272, (32, 3199): 226.3688364741416, (32, 3200): 225.9191200732244, (32, 3205): 229.31961399841623, (32, 3209): 226.2355476304156, (32, 3215): 225.85735377243336, (32, 3217): 225.1852952711022, (32, 3249): 225.8167271855395, (32, 3263): 230.85411442021623, (32, 3289): 227.1480331604503, (32, 3301): 227.56017509958227, (32, 3302): 227.22540066965004, (32, 3307): 226.8967610226451, (32, 3310): 227.85002476663783, (32, 3391): 233.3884173086506, (32, 3509): 114.19001160911729, (32, 3510): 113.71915201832967, (32, 3511): 113.86679789110573, (32, 3512): 113.43015919468495, (32, 3514): 113.39803024602408, (32, 3519): 116.10684263471306, (32, 3536): 114.73074900622177, (32, 3545): 115.30588990322414, (32, 3548): 114.36649985348538, (32, 3572): 115.19899600695211, (32, 3581): 115.18050133993697, (32, 3583): 114.17736159265733, (32, 3601): 117.24812410019277, (32, 3656): 117.1258876999183, (32, 3669): 117.61358396566196, (32, 3670): 118.09177107696105, (32, 3695): 115.11181072305354, (32, 3696): 115.41696239205172, (32, 3782): 111.7427436696034, (32, 3792): 111.63884920078091, (32, 3989): 133.1886784887448, (32, 4008): 136.04059379825537, (32, 4031): 136.46467051054987, (32, 4045): 134.87208091519048, (32, 4144): 134.45782712895647, (32, 4145): 130.97515283105957, (32, 4164): 133.20993915249514, (32, 4168): 132.03104583292966, (32, 4173): 131.7054695828109, (32, 4181): 129.96709043963477, (32, 4228): 128.979510782116, (32, 4248): 127.37957775772624, (32, 4254): 108.94775354386768, (32, 4260): 109.30555150863357, (32, 4262): 110.12636633500387, (32, 4273): 110.09733720957821, (32, 4319): 98.83672855723741, (32, 4326): 98.5843460551695, (32, 4328): 98.79847747558323, (32, 4334): 99.16525341941883, (32, 4335): 98.87234469942713, (32, 4372): 75.4953835403251, (32, 4413): 84.30414125608104, (32, 4434): 75.10235264653681, (32, 4447): 76.16750591381948, (32, 4452): 75.23739981166817, (32, 4463): 58.72340419075545, (32, 4465): 59.2021613259252, (32, 4619): 85.85384118821455, (32, 4645): 87.60513004313869, (32, 4657): 87.38810935355353, (32, 4666): 86.7415428917886, (32, 4676): 88.02833220914869, (32, 4678): 88.27907877259331, (32, 4689): 87.49609295755883, (32, 4704): 93.90443275237111, (32, 4726): 111.07004530474163, (32, 4727): 110.75758940656334, (32, 4730): 110.14588013284559, (32, 4731): 110.36075560978777, (32, 4734): 110.48441173858322, (32, 4735): 110.22089724628181, (32, 4736): 110.3973467699606, (32, 4737): 109.91138566261932, (32, 4738): 110.00411984763961, (32, 4756): 110.33355876180981, (32, 4760): 108.61879612457625, (32, 4761): 108.73765569252983, (32, 4762): 108.22916674649332, (32, 4765): 108.78910165160725, (32, 4773): 111.6523321541073, (32, 4774): 111.42134745563796, (32, 4790): 111.43773090370016, (32, 4795): 111.1533481695086, (32, 4799): 111.5823295654243, (32, 4801): 112.30675439542306, (32, 4804): 111.20226052903988, (32, 4805): 110.97004114427537, (32, 4806): 111.3749812002912, (32, 4815): 111.11914062033286, (32, 4816): 111.88084854012291, (32, 4817): 112.09561849659151, (32, 4826): 111.60940929606838, (32, 4830): 111.1893832794609, (32, 4839): 109.52595065894799, (32, 4840): 109.82439052331306, (32, 4841): 109.1865355751473, (32, 4846): 108.96277346714251, (32, 4848): 108.93498969039416, (32, 4850): 109.2251722846189, (32, 4871): 105.45157908384915, (32, 4883): 108.21143033606461, (32, 4900): 106.74001923910396, (32, 4901): 106.38400082402279, (32, 4917): 86.43439322305413, (32, 4931): 84.2089656197547, (32, 4944): 86.65091249203513, (32, 4956): 84.65301505480875, (32, 4958): 84.66241280584327, (32, 4959): 84.2921251933511, (32, 4961): 85.0744934381094, (32, 4966): 84.15126053514965, (32, 5207): 81.69242817636486, (32, 5272): 42.38647466580936, (32, 5283): 42.98252709551777, (32, 5287): 43.49366405847399, (32, 5289): 43.75746278560334, (32, 5293): 43.034288812042476, (32, 5295): 44.75136176553574, (32, 5296): 44.42943592369709, (32, 5298): 44.24198667247872, (32, 5303): 44.53577503860616, (32, 5305): 41.41421288457724, (32, 5306): 40.49870395958636, (32, 5307): 41.06065190837522, (32, 5308): 41.610093052126594, (32, 5313): 41.964741251636525, (32, 5314): 42.47759157772352, (32, 5317): 41.42690892020046, (32, 5319): 43.83907385298994, (32, 5324): 43.69485807079461, (32, 5326): 43.63108174120643, (32, 5348): 40.104940268677005, (32, 5351): 40.22934609982509, (32, 5399): 43.774010606553375, (32, 5413): 40.62441888057296, (32, 5422): 44.378500720277025, (32, 5445): 42.733324227791854, (32, 5448): 42.09832820745564, (32, 5456): 41.6698501080648, (32, 5467): 42.199305328588224, (32, 5624): 36.82112922237906, (32, 5671): 60.35021595847002, (32, 5672): 59.54272807945474, (32, 5797): 70.87354764156179, (32, 5871): 52.788039797967905, (32, 5976): 43.92266287513598, (32, 6118): 183.55870372431627, (32, 6248): 197.83171313008413, (32, 6345): 64.86927220353685, (32, 6352): 65.47170065031564, (32, 6354): 64.45923640492913, (32, 6359): 64.84620115533676, (32, 6376): 66.5799064210618, (32, 6378): 64.5796711224264, (32, 6381): 65.23104777719034, (32, 6383): 64.79234718523213, (32, 6396): 67.24053557552135, (32, 6399): 65.45665462645118, (32, 6408): 64.95248770429315, (32, 6409): 63.35449591810425, (32, 6419): 62.35219989141607, (32, 6422): 63.838675542585506, (32, 6423): 63.815976694477875, (32, 6424): 63.04777700924167, (32, 6439): 62.729526736441414, (32, 6464): 62.47377210544011, (32, 6465): 62.97948926087587, (32, 6469): 63.85733363474679, (32, 6470): 64.11132876368956, (32, 6472): 64.86700125352748, (32, 6480): 62.810081094882015, (32, 6486): 60.25868378667372, (32, 6497): 60.99805914611841, (32, 6503): 59.80355488559045, (32, 6508): 61.19129692165571, (32, 6509): 60.44295815326893, (32, 6521): 61.78102552157503, (32, 6544): 60.45558788890856, (32, 6552): 61.40211230408042, (32, 6553): 61.34862299298328, (32, 6554): 61.31466013946245, (32, 6578): 61.69511242529282, (32, 6582): 60.2555359969274, (32, 6601): 61.416609289106155, (32, 6609): 63.11177810007566, (32, 6610): 62.821646252096926, (32, 6611): 63.597508257307005, (32, 6614): 64.04460751953354, (32, 6615): 63.780558601551164, (32, 6616): 62.80590503219037, (32, 6617): 63.146650757876344, (32, 6618): 62.17194870227371, (32, 6619): 63.874022978505934, (32, 6620): 62.327322378890265, (32, 6621): 62.20837185807115, (32, 6622): 62.54535306215531, (32, 6623): 63.52064167910226, (32, 6624): 63.00331348125546, (32, 6625): 63.25871262638259, (32, 6626): 64.0821465538326, (32, 6627): 64.45818017102542, (32, 6628): 61.834186516907835, (32, 6629): 62.41890785322816, (32, 6630): 64.01352835170435, (32, 6632): 62.68364907971238, (32, 6634): 63.69181348688462, (32, 6635): 62.46063235794673, (32, 6636): 62.641175686717695, (32, 6637): 62.34245128434566, (32, 6638): 63.55928275616254, (32, 6639): 64.18098029775098, (32, 6640): 63.80412535600381, (32, 6641): 61.83189735023765, (32, 6642): 63.24033130684192, (32, 6643): 64.42105800034436, (32, 6645): 63.65869704662095, (32, 6646): 62.54089171027514, (32, 6647): 63.422287438490386, (32, 6653): 63.927084682990206, (32, 6655): 64.33646760586961, (32, 6658): 63.5033811804704, (32, 6662): 62.8962912715792, (32, 6819): 58.00958501714055, (32, 6996): 49.58397526461645, (32, 7059): 49.541567166777746, (32, 7187): 33.427392096664065, (32, 7304): 45.07764331221011, (32, 7528): 42.50659116299378, (32, 7720): 52.83002469286032, (32, 7793): 50.24058406003803, (32, 7807): 51.15697889888034, (32, 7808): 49.64111138590353, (32, 7831): 60.03656870434713, (32, 7850): 63.113625215817635, (32, 7852): 63.584616032017735, (32, 8012): 55.766332674766296, (32, 8125): 41.61746246859889, (32, 8208): 56.00276985523016, (32, 8392): 53.26561084597599, (32, 8651): 64.09259644657531, (32, 9088): 67.63455851137095, (32, 9443): 49.38403961258011, (32, 9444): 48.664743517901826, (32, 9828): 59.14537758826737, (32, 9868): 64.66301025116297, (32, 10180): 40.91707972173012, (32, 10256): 47.424418034530284, (32, 10276): 45.72467497191476, (32, 10378): 51.80597655232609, (32, 10676): 30.83288908205494, (32, 10714): 24.235624995510033, (32, 10730): 31.410343038770204, (32, 10862): 45.201559912585275, (32, 10881): 46.09772606282949, (32, 10883): 46.21649382626804, (32, 10885): 44.95809575502378, (32, 10891): 46.41197922328879, (32, 10909): 45.806045114812186, (32, 10911): 45.39402971789005, (32, 10913): 45.35812039495061, (32, 10915): 45.07010377340935, (32, 10919): 44.963885414861025, (32, 11037): 47.27483903423281, (32, 11039): 43.4682792650219, (32, 11516): 169.0148139765619, (32, 11856): 99.40080312439123, (32, 11857): 98.53241264944849, (32, 11861): 98.9687263943078, (32, 11881): 99.19813901667118, (32, 11902): 97.5083009410444, (32, 11911): 97.71314254118896, (32, 11914): 97.7235092989143, (32, 11922): 98.8008582931853, (32, 11924): 99.32851356707982, (32, 11926): 98.87185145364921, (32, 11950): 100.38645299593347, (32, 11963): 101.89611315534108, (32, 11983): 101.73171855094496, (32, 11985): 102.61139868589993, (32, 12009): 103.06056603088945, (32, 12010): 101.80143275304022, (32, 12018): 102.08122019157916, (32, 12020): 102.26333094194385, (32, 12021): 102.52509145602642, (32, 12024): 103.5566437599281, (32, 12025): 103.05374697687995, (32, 12027): 102.84725531837779, (32, 12031): 101.6170741255414, (32, 12032): 101.85480677197927, (32, 12035): 103.16689837120099, (32, 12041): 102.30805002006387, (32, 12045): 88.96872633830989, (32, 12145): 96.23723287712157, (32, 12275): 135.71432025956028, (32, 12294): 133.90727265101725, (32, 12358): 143.25134803522474, (32, 12463): 147.48235084798273, (32, 12465): 147.43782009338238, (32, 12482): 148.08401396554132, (32, 12503): 148.08207325329343, (32, 12506): 148.45577781406183, (32, 12549): 146.70371459850188, (32, 12559): 146.6061571222191, (32, 12569): 147.24705645463266, (32, 12572): 147.5088313651049, (32, 12574): 146.85773206285876, (32, 12576): 146.91583088298148, (32, 12591): 146.31088931212082, (32, 12608): 148.1914266684316, (32, 12696): 144.2028756844697, (32, 12710): 145.62637968371806, (32, 12728): 145.3409609507199, (32, 12766): 88.14048196411267, (32, 12771): 82.83221871767161, (32, 12790): 82.63534210258337, (32, 12795): 82.57548288542371, (32, 12797): 77.69789031516727, (32, 12798): 77.98466158774292, (32, 12811): 80.59730609543091, (32, 12830): 80.29824799353241, (32, 12848): 79.57528136351749, (32, 12850): 79.09269071232887, (32, 12852): 79.82116261525566, (32, 12854): 79.43223218253844, (32, 12859): 79.66160037272155, (32, 12861): 78.14426632305982, (32, 12865): 81.59757440561123, (32, 12866): 81.04975373721466, (32, 12867): 82.15272077394067, (32, 12874): 81.66533543751746, (32, 12875): 81.81859265451114, (32, 12881): 80.99041887078458, (32, 12883): 81.43512009774344, (32, 12885): 82.15788884096561, (32, 12888): 80.9822192281377, (32, 12889): 80.64690423821605, (32, 12892): 81.88236762000294, (32, 12893): 81.23752688969289, (32, 12896): 81.2303206319247, (32, 12906): 82.74344938425571, (32, 13018): 85.87251479994227, (32, 13071): 87.37146854918012, (32, 13131): 78.88085665946679, (32, 13146): 79.8688990923447, (32, 13159): 84.62816557633599, (32, 13193): 78.03100367213966, (32, 13198): 71.92827601627849, (32, 13292): 75.38965501381598, (32, 13296): 74.08941861853451, (32, 13406): 74.34130437156247, (32, 13407): 74.60239181835762, (32, 13417): 77.22591563110674, (32, 13418): 77.98809605965774, (32, 13438): 77.04832189056383, (32, 13442): 76.3826297298821, (32, 13443): 76.24722667857334, (32, 13764): 91.61576819084873, (32, 13766): 91.4563058381713, (32, 13771): 92.7319907063483, (32, 13783): 89.87947423215716, (32, 13784): 90.80244441048177, (32, 13792): 94.72859490565217, (32, 13824): 90.21938525681966, (32, 14017): 82.72467438144785, (32, 14870): 34.26154520086409, (32, 14997): 32.68503506904466, (32, 15000): 32.035744830233746, (32, 15003): 31.306040030098025, (32, 15006): 33.93485487775657, (32, 15007): 33.79503798491575, (32, 15056): 31.88796109179252, (32, 15063): 31.57866357975915, (32, 15069): 30.878149977614054, (32, 15076): 33.33060618426154, (32, 15086): 34.39867274774883, (32, 15087): 33.604381032007225, (32, 15111): 34.55551079039076, (32, 15116): 33.938251205062045, (32, 15722): 39.03501631572375, (32, 15998): 31.042558211159164, (32, 16073): 158.92377428136157, (32, 16939): 182.89597643992892, (32, 16940): 182.19153974485212, (32, 16951): 183.33119384349072, (32, 16963): 183.31525634396561, (32, 16965): 184.02390273751863, (32, 16969): 184.02827610093422, (32, 16970): 183.50609695768102, (32, 16971): 182.8553004578696, (32, 16973): 182.93376658979, (32, 16974): 184.4253974275742, (32, 16976): 183.4796284566472, (32, 16978): 182.96135681715649, (32, 16980): 183.61715552318594, (32, 16982): 184.5474519864916, (32, 17045): 215.46706186399697, (32, 17048): 216.3788027784803, (32, 17304): 122.51101972726711, (32, 17305): 122.5180670178163, (32, 17330): 122.79765988249525, (32, 17334): 121.56714153552151, (32, 17343): 123.53492206080018, (32, 17345): 122.00775990136879, (32, 17347): 123.04585972919647, (32, 17351): 120.39492032278388, (32, 17372): 121.64920706872837, (32, 17373): 123.41240310202022, (32, 17377): 123.57470638194586, (32, 17382): 122.526356838849, (32, 17383): 122.5632966602281, (32, 17389): 121.98263197562045, (32, 17400): 122.9729032578217, (32, 17401): 122.87753631967489, (32, 17402): 123.08023788974917, (32, 17403): 123.2228868727245, (32, 17440): 122.58652299023267, (32, 17455): 123.66274051062682, (32, 17491): 124.11274376333358, (32, 17507): 119.85854098257226, (32, 17509): 120.30839116982631, (32, 17590): 120.54640060056045, (32, 17615): 114.40034646269194, (32, 17642): 115.19967042539885, (32, 17643): 115.32673723887713, (32, 17668): 114.26723434712405, (32, 17721): 111.94598432621612, (32, 17754): 117.0447193040939, (32, 17769): 119.52208198855402, (32, 17776): 118.11688326219904, (32, 17804): 120.36046370969818, (32, 17809): 120.92709764468744, (32, 17824): 120.27083910594156, (32, 17837): 119.99091887520423, (32, 17838): 120.3156604693298, (32, 17862): 120.02352273894863, (32, 17866): 121.09591428862218, (32, 17872): 119.45912602591167, (32, 17873): 118.70134980668092, (32, 17881): 119.90422534342632, (32, 17947): 122.83574765791052, (32, 17951): 121.81272044709611, (32, 17953): 121.48959578762394, (32, 17954): 121.47758813973753, (32, 17959): 122.84415995577142, (32, 17963): 122.70802284655477, (32, 18000): 117.1939772204112, (32, 18001): 117.217010915158, (32, 18111): 127.97927888748053, (32, 18148): 98.16523123603397, (32, 18166): 109.01322730230278, (32, 18189): 120.44022170888474, (32, 18239): 123.52163997030667, (32, 18240): 123.56440984958209, (32, 18245): 123.60007241265114, (32, 18247): 123.52917661178333, (32, 18251): 123.65820761066412, (32, 18256): 123.85579939515031, (32, 18258): 123.74265858076899, (32, 18259): 123.7949208496416, (32, 18260): 123.88735052396419, (32, 18262): 124.02652511577301, (32, 18263): 123.92122610030262, (32, 18264): 124.00995645761581, (32, 18266): 124.11276655762933, (32, 18267): 124.19264261881818, (32, 18268): 124.25048328339399, (32, 18269): 124.41500341538219, (32, 18275): 124.33760559379844, (32, 18285): 123.9602239225246, (32, 18308): 122.23552854855842, (32, 18313): 121.79026793488923, (32, 18314): 122.14739046692691, (32, 18315): 124.26922525888638, (32, 18316): 124.32372729992258, (32, 18317): 124.40485544191877, (32, 18320): 124.38493572384253, (32, 18321): 124.45952482322251, (32, 18322): 124.57382572040859, (32, 18324): 124.57215137447987, (32, 18325): 124.8353265970519, (32, 18326): 124.73421977920482, (32, 18327): 124.5348172285029, (32, 18329): 124.87947537520344, (32, 18330): 124.9544303149534, (32, 18331): 124.74563077768781, (32, 18332): 124.56490190096014, (32, 18333): 124.86788006063426, (32, 18336): 124.62087383875401, (32, 18337): 124.66794095821628, (32, 18403): 124.908412370121, (32, 18432): 123.299733592604, (32, 18451): 124.39377325308831, (32, 18466): 125.30321396593966, (32, 18481): 124.16158611110643, (32, 18483): 124.20856905750462, (32, 18484): 124.02759003391924, (32, 18485): 123.43469711838824, (32, 18486): 123.6547172821975, (32, 18487): 123.26009010851362, (32, 18489): 123.77468336460356, (32, 18490): 123.98274782661917, (32, 18491): 124.14136422428561, (32, 18492): 122.96083879606884, (32, 18493): 123.54175866889211, (32, 18494): 123.74859590551243, (32, 18495): 123.85745021537824, (32, 18496): 123.73008950036214, (32, 18497): 123.12528646339263, (32, 18498): 123.39602859491289, (32, 18499): 123.6609438991787, (32, 18501): 123.38524743288468, (32, 18502): 123.21025771702998, (32, 18503): 123.13391940056017, (32, 18504): 123.85425681809018, (32, 18506): 123.2739453119196, (32, 18507): 123.0799979862272, (32, 18508): 123.57793848511717, (32, 18509): 123.53623313760981, (32, 18510): 123.07172428530261, (32, 18511): 123.49589302623428, (32, 18512): 123.38642002962318, (32, 18515): 123.80280520476201, (32, 18516): 123.65989426259857, (32, 18517): 123.37083548385313, (32, 18518): 123.84104983894447, (32, 18519): 123.91815182274219, (32, 18520): 123.58481953266751, (32, 18522): 124.7241353059674, (32, 18523): 124.70767482071192, (32, 18532): 124.86229210945186, (32, 18535): 124.48776872644869, (32, 18537): 124.27934553408953, (32, 18539): 124.29569890153273, (32, 18540): 124.29118394365375, (32, 18541): 124.37004111621172, (32, 18542): 124.42509205604945, (32, 18543): 124.13044251270712, (32, 18546): 124.18184674915355, (32, 18555): 124.50408247416384, (32, 18556): 124.52728378511377, (32, 18565): 124.76792258190157, (32, 18567): 124.75995007422435, (32, 18568): 124.62780440994638, (32, 18577): 125.91313585997703, (32, 18583): 125.84004786406959, (32, 18605): 126.28205521394428, (32, 18608): 124.66208907819231, (32, 18616): 127.47280173949834, (32, 18618): 128.3981103816581, (32, 18625): 128.42800672614092, (32, 18645): 127.68470326460024, (32, 18646): 127.79379405389207, (32, 18653): 126.5807649351474, (32, 18654): 127.38491869859668, (32, 18655): 126.77823476451621, (32, 18666): 130.72769235414802, (32, 18837): 132.88098001198267, (32, 18974): 125.62162272312001, (32, 18999): 127.14297637365479, (32, 19000): 127.46277636124354, (32, 19174): 116.71469425928333, (32, 19342): 124.21565540870893, (32, 19455): 115.88704912724465, (32, 19555): 103.55563266323414, (32, 19564): 106.65085162625813, (32, 19573): 105.55385620825278, (32, 19586): 104.91734771621815, (32, 19605): 104.78754998932504, (32, 19611): 105.44328487367243, (32, 19614): 104.53386496042882, (32, 19641): 112.82685380535125, (32, 19702): 113.35676592309426, (32, 19713): 112.60780259710535, (32, 19731): 97.88486471113568, (32, 19819): 114.82310083751283, (32, 19893): 71.3660904795685, (32, 19899): 74.02930737551029, (32, 19929): 72.36367733862436, (32, 19951): 78.8485955588359, (32, 19962): 72.28314295681264, (32, 19970): 74.89651547074084, (32, 19971): 74.64169349679301, (32, 19972): 73.89841241370989, (32, 19975): 73.84536724398399, (32, 19978): 81.4058013999825, (32, 19987): 81.69728404326844, (32, 19989): 79.88741926003466, (32, 20039): 82.11967816814044, (32, 20043): 83.13000792057487, (32, 20047): 82.7693363013004, (32, 20052): 80.5692888088185, (32, 20054): 80.60236292734514, (32, 20085): 91.45601159120116, (32, 20104): 92.09464435576173, (32, 20132): 87.95224495183912, (32, 20203): 68.51556045549839, (32, 20280): 67.0231174441389, (32, 20285): 66.53462639391853, (32, 20290): 67.49493919147544, (32, 20297): 66.90140558587868, (32, 20309): 80.16168879603035, (32, 20453): 91.85119480585574, (32, 20485): 63.207928276189456, (32, 20520): 61.85341897859326, (32, 20526): 60.38397499149066, (32, 20698): 115.5920327178308, (32, 20868): 128.37860666002607, (32, 21042): 65.85085003622692, (32, 21057): 70.05066770616443, (32, 21066): 67.308572113662, (32, 21075): 67.49414571922169, (32, 21093): 65.21476324230927, (32, 21098): 66.87113031692502, (32, 21127): 65.68628375315842, (32, 21130): 66.0119574740219, (32, 21144): 66.78207558295998, (32, 21146): 65.42005924901147, (32, 21147): 66.98095286928297, (32, 21148): 67.3864870590492, (32, 21153): 69.25701739829246, (32, 21293): 71.64071644061053, (32, 21426): 79.04514956533846, (32, 21442): 84.91673620953463, (32, 21451): 85.44457032702499, (32, 21466): 81.50528682063815, (32, 21469): 81.95646813346512, (32, 21471): 81.2968249027444, (32, 21473): 81.56329233010625, (32, 21475): 81.20886764330892, (32, 21482): 82.58831225691277, (32, 21484): 82.31189471631457, (32, 21488): 82.14069062720031, (32, 21494): 80.72271180420687, (32, 21498): 81.18248105807992, (32, 21500): 80.0742338653658, (32, 21514): 79.4481093806658, (32, 21537): 78.88407921135403, (32, 21662): 78.74441729671028, (32, 21691): 76.47524296066166, (32, 21757): 76.31234515321148, (32, 21777): 55.06686433098672, (32, 21778): 54.537907701031, (32, 21779): 54.35578426498949, (32, 21790): 56.18107748521697, (32, 21802): 55.22728775120091, (32, 21824): 55.328783190629736, (32, 21874): 53.912973288643414, (32, 21879): 52.730530538393715, (32, 21983): 59.775136385741156, (32, 22002): 62.77629608089167, (32, 22132): 69.76094853806713, (32, 22261): 57.19722222836829, (32, 22298): 55.298379653383556, (32, 22339): 62.7954863564245, (32, 22508): 43.776802634879715, (32, 22841): 241.8039800669246, (32, 22842): 241.71620725755528, (32, 22874): 239.65946435714372, (32, 22941): 240.14934667642157, (32, 22956): 241.13529470736222, (32, 22960): 241.66853057996607, (32, 22968): 241.46830299803926, (32, 22970): 241.94108176705805, (32, 22974): 241.67743256412984, (32, 22980): 242.94911812203844, (32, 23025): 241.68283833132799, (32, 23028): 241.16298944709274, (32, 23081): 241.89394127488782, (32, 23104): 237.6496232985199, (32, 23147): 229.65938908688972, (32, 23298): 87.62414209238712, (32, 23376): 85.66759298900443, (32, 23381): 82.68423772136498, (32, 23529): 87.42807510481146, (32, 23556): 86.50887700334779, (32, 23718): 87.94661178891438, (32, 24001): 99.73018849302632, (32, 24094): 100.7258462250649, (32, 24129): 102.75070821839533, (32, 24174): 97.50007969747259, (32, 24235): 101.34108121246331, (32, 24259): 103.94843714583273, (32, 24260): 103.70184033114525, (32, 24261): 103.3603712526477, (32, 24305): 106.54816079307238, (32, 24306): 106.80918898120827, (32, 24307): 106.29271793514177, (32, 24308): 106.53186864967033, (32, 24498): 113.65797682264886, (32, 24499): 113.65483280683351, (32, 24500): 113.33160048599187, (32, 24668): 113.4085571119413, (32, 24711): 115.1300683910743, (32, 24756): 115.67303711823578, (32, 24788): 116.59509530359719, (32, 24809): 113.5301698082501, (32, 24813): 114.5530702643284, (32, 24821): 114.24718025519827, (32, 24825): 114.34342535239698, (32, 24832): 113.42659397284999, (32, 24833): 113.81909930823532, (32, 24835): 114.17070923391971, (32, 24837): 114.88743710611121, (32, 24840): 113.31839483441979, (32, 24841): 114.02308047164222, (32, 24844): 113.272143233585, (32, 24845): 113.88058805254673, (32, 24846): 113.49397079256056, (32, 24849): 113.67733851319925, (32, 24850): 114.59448626300984, (32, 24863): 109.6065710993283, (32, 24866): 110.33170366261253, (32, 24885): 110.9456488470581, (32, 24886): 110.86585509248756, (32, 24889): 112.91018964428798, (32, 24903): 113.72828253439722, (32, 24909): 111.51377594452671, (32, 24999): 143.44096506311527, (32, 25019): 143.14260300776024, (32, 25028): 142.91253425605072, (32, 25137): 66.17875592029517, (32, 25145): 67.02227045313064, (32, 25208): 75.5641320579613, (32, 25233): 74.40930595403302, (32, 25371): 67.38471356224738, (32, 25377): 65.42079287221075, (32, 25828): 25.66195443622265, (32, 25851): 22.92151271615085, (32, 25874): 26.804960292939697, (32, 25898): 27.27806536656355, (32, 25946): 25.220206230495947, (32, 26047): 35.14579385820459, (32, 26066): 55.38099059359945, (32, 26197): 43.019802587709556, (32, 26212): 12.5, (32, 26253): 12.5, (32, 26254): 12.5, (32, 26257): 12.5, (32, 26258): 12.5, (32, 26260): 12.5, (32, 26266): 12.5, (32, 26267): 12.5, (32, 26271): 12.5, (32, 26304): 12.5, (32, 26305): 12.5, (32, 26363): 21.720583625975127, (32, 26441): 54.910932290852095, (32, 26442): 54.73054054166783, (32, 26450): 53.51916891979578, (32, 26459): 53.160782231842155, (32, 26462): 53.22200233473088, (32, 26467): 56.737115272729866, (32, 26471): 55.873365742275645, (32, 26472): 55.8059412745188, (32, 26473): 55.801730968952576, (32, 26476): 55.64569828882758, (32, 26485): 53.88451728022631, (32, 26493): 54.05985204314053, (32, 26524): 53.64602843916829, (32, 26525): 53.57076660664762, (32, 26556): 55.38635368843248, (32, 26560): 55.07305423596079, (32, 26561): 54.26942759631748, (32, 26564): 55.11930281282707, (32, 26569): 54.14638598827465, (32, 26570): 53.91835905965365, (32, 26573): 54.22148262013086, (32, 26581): 54.29693846719991, (32, 26583): 53.97022435963424, (32, 26593): 54.44200330576385, (32, 26837): 57.07363200809095, (32, 26844): 57.8308076332083, (32, 26863): 56.44453148881695, (32, 26893): 58.71265482998335, (32, 26902): 59.742951142650384, (32, 26905): 58.47267181970953, (32, 26912): 59.350177736343745, (32, 26921): 57.51408417379545, (32, 26922): 55.88627088662642, (32, 27212): 62.369813890328956, (32, 27218): 61.59502705067591, (32, 27239): 63.86896488356047, (32, 27257): 63.007859286419716, (32, 27274): 64.1465505547864, (32, 27279): 63.90886768561114, (32, 27282): 63.006741279159435, (32, 27283): 63.49416987412304, (32, 27285): 64.51525776302812, (32, 27286): 63.57653021925299, (32, 27290): 62.224884399817974, (32, 27295): 61.77107185928049, (32, 27300): 64.32862960429465, (32, 27344): 61.623638193559415, (32, 27366): 62.590469475555004, (32, 27383): 64.46161372381425, (32, 27398): 65.71688190167436, (32, 27406): 64.86835578579837, (32, 27407): 65.18910653685627, (32, 27426): 64.52958421350228, (32, 27432): 60.482453164479665, (32, 27460): 63.09589310932874, (32, 27523): 62.287264777816894, (32, 27545): 79.05554643874034, (32, 27602): 99.3946438852866, (32, 27606): 99.80633019897981, (32, 27646): 77.86045190721691, (32, 27667): 81.99848596776789, (32, 27672): 82.21922342835451, (32, 27674): 81.51141864532589, (32, 27688): 82.1242551438213, (32, 27692): 82.93092801792562, (32, 27693): 82.31073700640869, (32, 27705): 82.27560086881746, (32, 27712): 82.57933182133483, (32, 27786): 101.62917294781923, (32, 27790): 100.04894879734957, (32, 27791): 99.97120202041557, (32, 27795): 100.43479732270906, (32, 27801): 99.17316610805983, (32, 27813): 102.18510586727562, (32, 27816): 101.5679359745631, (32, 27823): 99.13337894631407, (32, 27830): 100.82254483890918, (32, 27884): 70.95564928565318, (32, 27885): 76.11584428197062, (32, 27896): 72.98584505569372, (32, 27919): 72.7700541261604, (32, 27922): 73.41435417807998, (32, 27930): 71.72945140778008, (32, 27934): 71.92978931389703, (32, 27935): 72.07982908255802, (32, 27948): 97.28602493774389, (32, 27951): 98.20412999358523, (32, 28061): 87.60978659364696, (32, 28290): 126.11971353786181, (32, 28292): 127.2757993564307, (32, 28293): 126.36864400911143, (32, 28295): 126.2087579088477, (32, 28296): 126.18005332934023, (32, 28297): 125.52934347367672, (32, 28302): 125.40150266739258, (32, 28310): 163.2192343442649, (32, 28313): 164.59098562187825, (32, 28372): 163.29251193160528, (32, 28398): 163.46335510772983, (32, 28399): 163.28541478765575, (32, 28400): 163.75766767203172, (32, 28401): 162.34117682835142, (32, 28445): 164.62278872204485, (32, 28475): 160.40726742108612, (32, 28885): 97.17142990404722, (32, 28886): 96.61666143232074, (32, 28915): 96.2531220059164, (32, 28916): 96.15070985444743, (32, 28917): 95.7938035211522, (32, 28921): 98.03272677216881, (32, 28931): 97.74435163807232, (32, 28945): 93.53760675470112, (32, 28982): 94.75915139408775, (32, 29219): 93.42094038131975, (32, 29228): 91.85723568149939, (32, 29246): 100.61598569503404, (32, 29248): 99.91957960107221, (32, 29282): 97.91554358470616, (32, 29290): 102.2330992457657, (32, 29291): 101.65249696724833, (32, 29292): 102.11585405592771, (32, 29293): 101.30862589669069, (32, 29294): 101.71409601301578, (32, 29298): 101.22118349892693, (32, 29299): 101.00196585517286, (32, 29304): 100.58231909168828, (32, 29317): 98.86343066043088, (32, 29323): 98.7486520997962, (32, 29330): 99.54599299781196, (32, 29331): 100.07322535923458, (32, 29344): 92.34790157238713, (32, 29445): 71.62187561022266, (32, 29724): 242.19408088225265, (32, 29738): 242.5254852446345, (32, 29745): 241.68375699519834, (32, 29748): 242.50987578560174, (32, 29750): 243.319363369091, (32, 29759): 241.97754193703653, (32, 29772): 243.21257714477926, (32, 29781): 242.9611698796083, (32, 29784): 242.47713407113216, (32, 29790): 243.34200667293305, (32, 29811): 242.9213421233543, (32, 29817): 246.86730662416286, (32, 29818): 246.63382855380215, (32, 29929): 241.1726690969655, (32, 30039): 243.750110149591, (32, 30066): 239.9457532046223, (32, 30116): 230.0098938921584, (32, 30238): 215.30480122769436, (32, 30248): 220.67327020405966, (32, 30260): 220.6769827437103, (32, 30545): 94.053897461393, (32, 30733): 79.63531786976787, (32, 30756): 70.91482722147526, (32, 30921): 80.27087044138261, (32, 31079): 79.51559878912869, (32, 31149): 72.8980629545458, (32, 31154): 73.82270802959776, (32, 31160): 72.7020481587116, (32, 31163): 73.65800011826867, (32, 31189): 67.698980859571, (32, 31215): 68.88980080125333, (32, 31259): 72.56404228511734, (32, 31262): 71.749084709411, (32, 31430): 82.6447723863955, (32, 31568): 79.02742348299776, (32, 31751): 79.02612385988473, (38, 109): 110.60301091547953, (38, 872): 277.0252722702388, (38, 873): 277.9193952202319, (38, 877): 277.57784504318647, (38, 879): 277.7098738431933, (38, 884): 276.797549237236, (38, 889): 277.36088349147, (38, 891): 276.5034374505556, (38, 892): 278.40423380415945, (38, 894): 278.29389323264263, (38, 896): 277.44243852559106, (38, 903): 277.60428224289325, (38, 909): 276.1018647143626, (38, 910): 276.46543435513433, (38, 912): 275.87262386249233, (38, 913): 275.2174344621977, (38, 916): 274.9479950418307, (38, 926): 276.7658770395049, (38, 927): 276.46672519876444, (38, 948): 276.18039073208433, (38, 961): 276.7211163170258, (38, 962): 276.8264738436875, (38, 963): 276.9436263101651, (38, 967): 277.984837443581, (38, 974): 277.49020287896695, (38, 998): 278.3333805361014, (38, 1014): 297.9465425207027, (38, 1086): 274.9270870613934, (38, 1087): 274.81623452007665, (38, 1089): 273.9868724805935, (38, 1090): 274.3652023699519, (38, 1092): 275.6593464932087, (38, 1097): 274.6717726292106, (38, 1107): 276.3049083047986, (38, 1387): 139.2696499076911, (38, 1554): 125.24236676361713, (38, 1827): 317.5357056461144, (38, 1828): 317.6380604578157, (38, 1829): 317.76958014389385, (38, 1830): 317.59179760065604, (38, 1831): 317.6783138951153, (38, 1832): 317.58592125832405, (38, 1833): 317.6029826268916, (38, 1836): 317.5072760965385, (38, 1841): 318.06923726332997, (38, 1843): 317.8299314268126, (38, 1844): 317.93021317967435, (38, 1845): 317.6397820540255, (38, 1847): 316.73587900149175, (38, 1848): 317.05124352498717, (38, 1849): 318.52279920938525, (38, 1850): 318.68341318143325, (38, 1851): 317.2758609474478, (38, 1852): 317.28440640856144, (38, 1854): 317.44695831740233, (38, 1856): 316.67194689342045, (38, 1857): 317.0218306589409, (38, 1858): 318.3892508982643, (38, 1861): 317.7372719975216, (38, 1866): 316.63925288716155, (38, 1867): 318.0979497065101, (38, 1868): 317.91756150337596, (38, 1870): 317.88502493436016, (38, 1871): 318.0666381100492, (38, 1875): 317.44076120577796, (38, 1880): 316.88263227042967, (38, 1882): 316.95531781208126, (38, 1883): 318.7122185205356, (38, 1889): 317.07181433528945, (38, 1893): 317.81005499709937, (38, 1894): 317.58970066868903, (38, 1899): 316.88368560434674, (38, 1900): 317.05381307619416, (38, 1902): 318.1993012825864, (38, 1905): 318.47938114019075, (38, 1907): 317.28131541634065, (38, 1910): 317.4055260011802, (38, 1917): 319.13428707557676, (38, 1920): 317.31551078309957, (38, 1935): 318.54601431610774, (38, 1937): 318.7880193004445, (38, 1946): 316.4163813808669, (38, 1949): 316.6997293385593, (38, 1950): 315.69456327772167, (38, 1951): 316.17215200774, (38, 1952): 316.4873613422814, (38, 1953): 316.67258086055045, (38, 1954): 316.42785611609975, (38, 1958): 316.60658014088096, (38, 1960): 317.0676516513715, (38, 1968): 317.24965933078994, (38, 1969): 318.6291399161182, (38, 1974): 318.2661076228649, (38, 1975): 318.25376346174454, (38, 1979): 317.6020773171594, (38, 1980): 317.5242636528629, (38, 1981): 317.7356063849189, (38, 1985): 317.9035646199949, (38, 1994): 315.2569471540555, (38, 2011): 316.93438878148345, (38, 2019): 319.2281043426689, (38, 2020): 318.9246643735404, (38, 2029): 317.74610272376736, (38, 2030): 318.71475236888443, (38, 2032): 317.5397332111114, (38, 2033): 318.179155359081, (38, 2034): 318.1549432191772, (38, 2036): 316.9247740430305, (38, 2037): 317.24193607616576, (38, 2038): 317.40617889391336, (38, 2042): 320.9473433425146, (38, 2050): 318.0389577482452, (38, 2051): 317.9735772519703, (38, 2053): 318.07386664128273, (38, 2054): 318.3867361904792, (38, 2066): 317.7475245128409, (38, 2067): 317.7568523431314, (38, 2071): 314.6722660789511, (38, 2072): 315.2705174527129, (38, 2073): 313.68855921449557, (38, 2074): 313.6006945238546, (38, 2080): 312.58572951273106, (38, 2082): 315.5901629234271, (38, 2083): 315.9003102469547, (38, 2089): 315.262854239467, (38, 2090): 315.5542990125272, (38, 2092): 315.1733502830066, (38, 2098): 312.9824178321602, (38, 2099): 313.31843375990195, (38, 2101): 312.90978448569115, (38, 2102): 314.53217354717697, (38, 2103): 314.01773672345786, (38, 2104): 313.7313476163669, (38, 2106): 316.10124545541254, (38, 2112): 313.1156046802403, (38, 2113): 314.7566024066167, (38, 2114): 315.12922048662506, (38, 2117): 316.33501253146216, (38, 2123): 314.3125890858295, (38, 2124): 314.64702025994603, (38, 2134): 313.67825339587694, (38, 2138): 314.6687025284937, (38, 2141): 313.79909296481884, (38, 2148): 314.22128102904725, (38, 2150): 312.9821566498087, (38, 2151): 313.3295560527098, (38, 2152): 312.7929779993287, (38, 2153): 314.341051303437, (38, 2154): 312.95978987001746, (38, 2155): 312.78811717148096, (38, 2156): 312.5390078964573, (38, 2157): 312.8445059179723, (38, 2160): 315.105642278695, (38, 2161): 312.7289964218971, (38, 2162): 314.3714900700379, (38, 2163): 313.90417768620216, (38, 2164): 313.8681373236715, (38, 2168): 313.08417125445857, (38, 2172): 313.364507624413, (38, 2174): 313.28113391322637, (38, 2178): 313.62913294509445, (38, 2179): 313.4100074771358, (38, 2183): 314.63874771003395, (38, 2185): 314.6559781437142, (38, 2186): 314.3910620280028, (38, 2190): 315.17830307691395, (38, 2192): 314.7000253214196, (38, 2193): 314.734632360205, (38, 2194): 314.24596993094093, (38, 2195): 314.1671417541071, (38, 2197): 314.80061103691133, (38, 2205): 314.10483209987893, (38, 2207): 313.20189086469367, (38, 2208): 313.70518571217355, (38, 2212): 314.8947038712726, (38, 2214): 304.8739425941768, (38, 2225): 306.0161614018567, (38, 2231): 303.8956595766252, (38, 2278): 310.8028136584948, (38, 2284): 311.7865419418858, (38, 2285): 311.6371310844574, (38, 2291): 309.58031113689583, (38, 2292): 309.87133432072676, (38, 2307): 311.13142167228443, (38, 2313): 309.32027879409617, (38, 2317): 309.15708182661285, (38, 2319): 310.21009639856055, (38, 2321): 310.6595674145118, (38, 2323): 310.6191811825496, (38, 2326): 312.41398009875496, (38, 2327): 311.97890316699875, (38, 2329): 311.6799004561223, (38, 2330): 311.3345972999987, (38, 2332): 312.0419218642161, (38, 2344): 310.9609509013136, (38, 2346): 310.92693009869623, (38, 2361): 310.86644521659764, (38, 2368): 315.88164432474144, (38, 2374): 316.35006510795847, (38, 2375): 316.51706261489494, (38, 2377): 314.85529021788886, (38, 2378): 316.81279747569494, (38, 2379): 316.8409693710027, (38, 2380): 317.015924511642, (38, 2383): 315.3093570379818, (38, 2385): 315.5720905520596, (38, 2395): 315.61254399082986, (38, 2397): 316.63593353647286, (38, 2398): 314.32433272777945, (38, 2399): 314.9316776831541, (38, 2400): 314.79715017253324, (38, 2402): 315.7129209688449, (38, 2403): 316.0852360783782, (38, 2404): 316.18698228080865, (38, 2405): 315.2844612107362, (38, 2407): 316.02808689177243, (38, 2408): 316.459039721007, (38, 2409): 315.56044225017484, (38, 2411): 316.0583582912444, (38, 2412): 315.96980789005744, (38, 2413): 316.271883887321, (38, 2414): 315.7720310412067, (38, 2422): 315.93641059235125, (38, 2424): 316.08021791371226, (38, 2426): 316.1658005695684, (38, 2433): 315.46213545865777, (38, 2436): 315.26144047069124, (38, 2437): 313.09115640676436, (38, 2440): 313.5738240467403, (38, 2445): 323.04107285223097, (38, 2447): 321.8766949969278, (38, 2454): 322.9894879743802, (38, 2455): 323.0659291175269, (38, 2460): 319.590878941472, (38, 2461): 320.01662733597686, (38, 2471): 326.8264627013782, (38, 2492): 318.79060472790604, (38, 2511): 315.4719123437601, (38, 2523): 317.16723369897295, (38, 2525): 316.6010305535889, (38, 2535): 317.92019760998596, (38, 2537): 317.14347414065355, (38, 2538): 317.6991047763956, (38, 2539): 317.37702944791357, (38, 2540): 318.2700814199863, (38, 2542): 318.7981854559324, (38, 2559): 329.9056176916752, (38, 2575): 328.8033273137431, (38, 2599): 312.5469181756688, (38, 2600): 316.18647393628373, (38, 2607): 314.15107889449615, (38, 2627): 317.2018671261425, (38, 2647): 319.14168656391246, (38, 2674): 318.2329426529365, (38, 2681): 317.88917391365936, (38, 2683): 318.90436665783534, (38, 2686): 317.8015240686858, (38, 2689): 330.90867296930355, (38, 2690): 330.95710096353145, (38, 2713): 333.0247082083896, (38, 2714): 333.1793399024235, (38, 2715): 333.50640804129097, (38, 2739): 333.23600062731776, (38, 2740): 331.356434545573, (38, 2741): 331.5319030622667, (38, 2749): 332.71391315477456, (38, 2750): 332.8399339833064, (38, 2752): 333.08389689920443, (38, 2755): 333.32743471856435, (38, 2758): 333.2319569835262, (38, 2759): 333.2437890862464, (38, 2769): 332.89111023285636, (38, 2771): 331.83698644178725, (38, 2779): 331.7686204127178, (38, 2784): 328.0166654706477, (38, 2800): 328.5020774254968, (38, 2802): 330.6342640042731, (38, 2803): 330.530972254998, (38, 2804): 330.3209933527603, (38, 2805): 330.8457405158155, (38, 2807): 330.84675097878494, (38, 2809): 330.67734642740277, (38, 2812): 328.63559784494845, (38, 2814): 330.4236526591365, (38, 2817): 330.2979341026, (38, 2819): 330.9414684617174, (38, 2823): 328.6530288304618, (38, 2832): 331.2211656492479, (38, 2836): 329.75344188081147, (38, 2839): 330.8636830955836, (38, 2841): 330.4712978615342, (38, 2843): 330.3975110058317, (38, 2846): 329.95594788988524, (38, 2849): 331.4137954901443, (38, 2852): 331.09429462361993, (38, 2853): 331.55951300099895, (38, 2876): 331.6064394448606, (38, 2877): 332.76865949202266, (38, 2885): 332.9132690106371, (38, 2918): 331.2416583042444, (38, 2921): 331.72355380907, (38, 2925): 329.5245562311492, (38, 2926): 328.8242808679559, (38, 2930): 330.29583189331936, (38, 2931): 329.68875156583334, (38, 2938): 331.21233019640664, (38, 2940): 332.8495221440308, (38, 2947): 331.16324587739075, (38, 2949): 330.3616658905066, (38, 2950): 330.5543517249631, (38, 2952): 330.3034392442512, (38, 2958): 330.2691293388934, (38, 2959): 330.5503137272093, (38, 2960): 331.09348243031667, (38, 2961): 330.8102893789219, (38, 2963): 330.03717644279357, (38, 2968): 330.17534054205396, (38, 2976): 329.9919148754181, (38, 2981): 324.98010006276473, (38, 2982): 324.8000900307, (38, 2984): 324.54249800350755, (38, 3003): 324.05970520071327, (38, 3046): 321.2885128184887, (38, 3050): 323.618418552156, (38, 3051): 323.8300854743653, (38, 3053): 323.26601010798964, (38, 3069): 326.2532732273097, (38, 3071): 323.2274523047451, (38, 3080): 332.84407121323414, (38, 3199): 322.98524426829493, (38, 3200): 322.3772687421877, (38, 3205): 325.9673175407841, (38, 3209): 322.6745222057902, (38, 3215): 322.43702842695774, (38, 3217): 321.7183301945239, (38, 3249): 322.5275180469009, (38, 3263): 327.9647494625364, (38, 3289): 324.30843212587064, (38, 3301): 324.41983005279417, (38, 3302): 324.18345419567464, (38, 3307): 323.8672789587569, (38, 3310): 324.7291299538031, (38, 3391): 324.1199109314882, (38, 3509): 210.26442083853328, (38, 3510): 209.7568662315312, (38, 3511): 210.1251946675158, (38, 3512): 209.83766084891343, (38, 3514): 209.9681882540323, (38, 3519): 211.30567165389243, (38, 3536): 211.2130952974932, (38, 3545): 212.04001330387769, (38, 3548): 211.30070654320468, (38, 3572): 211.46471503832376, (38, 3581): 210.74840849779542, (38, 3583): 210.52776452483096, (38, 3601): 212.21141850237993, (38, 3656): 211.2688718881428, (38, 3669): 210.01637179879924, (38, 3670): 210.46046301118142, (38, 3695): 207.96922899892206, (38, 3696): 208.33342476012297, (38, 3782): 211.98419883343834, (38, 3792): 211.35233484952775, (38, 3989): 12.5, (38, 4008): 13.535258526175127, (38, 4031): 14.68634019614632, (38, 4045): 12.51694221915657, (38, 4144): 12.5, (38, 4145): 12.5, (38, 4164): 12.5, (38, 4168): 12.5, (38, 4173): 12.5, (38, 4181): 12.5, (38, 4228): 12.5, (38, 4248): 12.5, (38, 4254): 15.770538838636494, (38, 4260): 15.11649424245153, (38, 4262): 14.583338892927568, (38, 4273): 14.390788176512425, (38, 4319): 26.42173903462701, (38, 4326): 26.57954418071001, (38, 4328): 26.292550110073048, (38, 4334): 26.213727175523335, (38, 4335): 26.54647857208477, (38, 4372): 110.30524381020463, (38, 4413): 115.1534503559718, (38, 4434): 109.58537343552588, (38, 4447): 107.98287819568522, (38, 4452): 109.91693153284122, (38, 4463): 118.6719411642675, (38, 4465): 118.01106709468127, (38, 4619): 121.50027393761711, (38, 4645): 120.66678214577225, (38, 4657): 121.40527588775696, (38, 4666): 122.03918328818733, (38, 4676): 122.09434458720138, (38, 4678): 121.75130071523877, (38, 4689): 122.60477111760156, (38, 4704): 123.17985735857258, (38, 4726): 141.6739433312158, (38, 4727): 141.3911243901079, (38, 4730): 140.79436724655048, (38, 4731): 141.29010164756957, (38, 4734): 139.74062951268087, (38, 4735): 139.75310201068518, (38, 4736): 140.13120650716306, (38, 4737): 139.98769159138266, (38, 4738): 140.2473105766705, (38, 4756): 140.67830409827386, (38, 4760): 137.8967902653609, (38, 4761): 137.5040659303574, (38, 4762): 137.84852502813308, (38, 4765): 138.1996085571429, (38, 4773): 141.96074997664536, (38, 4774): 142.1552681999799, (38, 4790): 141.70547121193445, (38, 4795): 141.34617542452196, (38, 4799): 142.51419615379996, (38, 4801): 143.71757519238136, (38, 4804): 140.88201122631634, (38, 4805): 140.59326062746794, (38, 4806): 142.70655452923702, (38, 4815): 142.82878985659588, (38, 4816): 143.33329965209617, (38, 4817): 143.98634932205132, (38, 4826): 143.40709293326472, (38, 4830): 143.22544377835524, (38, 4839): 138.7398744664188, (38, 4840): 139.21328305566655, (38, 4841): 138.8024511548407, (38, 4846): 138.52049630304262, (38, 4848): 138.90506078717092, (38, 4850): 139.23575477618763, (38, 4871): 133.95242269461176, (38, 4883): 136.92782974740317, (38, 4900): 134.76031499284386, (38, 4901): 134.77548091080263, (38, 4917): 130.26770291900033, (38, 4931): 129.102414587973, (38, 4944): 130.06952608265573, (38, 4956): 129.64515726448244, (38, 4958): 130.2674802286908, (38, 4959): 130.49829579625253, (38, 4961): 129.6114613223513, (38, 4966): 129.7444627736364, (38, 5207): 128.56696313759093, (38, 5272): 94.2182475465983, (38, 5283): 94.4726799711301, (38, 5287): 96.41726195068817, (38, 5289): 96.59785621933035, (38, 5293): 92.78760564566382, (38, 5295): 93.29502316693579, (38, 5296): 94.21875034878582, (38, 5298): 94.72964365542417, (38, 5303): 95.69311646060616, (38, 5305): 95.90176040090782, (38, 5306): 97.06702535131949, (38, 5307): 95.88796406178768, (38, 5308): 96.28601575662698, (38, 5313): 95.11566787730406, (38, 5314): 94.88255680605862, (38, 5317): 96.8892894584603, (38, 5319): 95.71978705427385, (38, 5324): 94.89857066717327, (38, 5326): 94.31907058961008, (38, 5348): 97.81738204750964, (38, 5351): 99.24400383244289, (38, 5399): 98.07733067476737, (38, 5413): 101.54176571608181, (38, 5422): 97.26701915486095, (38, 5445): 97.21729836947834, (38, 5448): 97.05318870287363, (38, 5456): 97.99513362115572, (38, 5467): 98.40976461511312, (38, 5624): 94.01032613416065, (38, 5671): 87.3162975989703, (38, 5672): 86.77900154669946, (38, 5797): 94.07425040368967, (38, 5871): 110.40395552224051, (38, 5976): 107.78041233953887, (38, 6118): 269.53304461196484, (38, 6248): 279.6899211603716, (38, 6345): 94.59475623216011, (38, 6352): 96.98663835503775, (38, 6354): 94.01820626205732, (38, 6359): 93.53669179008027, (38, 6376): 96.60371705933422, (38, 6378): 94.29911131943028, (38, 6381): 93.72529097284855, (38, 6383): 95.1044824641929, (38, 6396): 93.98647332942924, (38, 6399): 94.55544680733317, (38, 6408): 96.90501894723066, (38, 6409): 95.8132446789323, (38, 6419): 99.70491802457214, (38, 6422): 96.61113444284774, (38, 6423): 96.80487863308662, (38, 6424): 94.29548060383236, (38, 6439): 94.76446905047547, (38, 6464): 95.43403880231433, (38, 6465): 95.65357062873773, (38, 6469): 95.32956665610213, (38, 6470): 95.4699267118304, (38, 6472): 92.72532929581739, (38, 6480): 93.28477520274132, (38, 6486): 92.01825817086548, (38, 6497): 92.43916608810439, (38, 6503): 95.40694857311341, (38, 6508): 95.1645219283122, (38, 6509): 94.74547598136857, (38, 6521): 93.03398539926151, (38, 6544): 93.26749266273225, (38, 6552): 96.28154794577084, (38, 6553): 96.6529769115608, (38, 6554): 97.0301393357955, (38, 6578): 95.65254888180723, (38, 6582): 95.99351825778848, (38, 6601): 95.49520758003985, (38, 6609): 92.46163622639995, (38, 6610): 92.36594897578861, (38, 6611): 92.26896255193024, (38, 6614): 92.45167528386861, (38, 6615): 92.38907088528578, (38, 6616): 92.03161629611272, (38, 6617): 92.18952376101345, (38, 6618): 91.68111661166623, (38, 6619): 92.72535334888133, (38, 6620): 92.04199382480729, (38, 6621): 92.3613353961543, (38, 6622): 92.27438749379057, (38, 6623): 92.4979460900838, (38, 6624): 92.79409364159321, (38, 6625): 92.845808820571, (38, 6626): 92.73873744095124, (38, 6627): 92.52201123500825, (38, 6628): 92.12863742773979, (38, 6629): 92.72662666448966, (38, 6630): 93.10010182689128, (38, 6632): 92.74931648938338, (38, 6634): 93.4489758169364, (38, 6635): 92.4644667842486, (38, 6636): 92.01993121378055, (38, 6637): 93.16224288627869, (38, 6638): 93.0712450194087, (38, 6639): 92.49411033628554, (38, 6640): 93.01236440798631, (38, 6641): 92.38569221157897, (38, 6642): 93.07215897958926, (38, 6643): 92.76869192160757, (38, 6645): 92.68602215588916, (38, 6646): 91.77882513402501, (38, 6647): 92.97197021552438, (38, 6653): 92.40002251741804, (38, 6655): 92.48764156183651, (38, 6658): 93.47675526707519, (38, 6662): 93.10052880989431, (38, 6819): 111.41266329023198, (38, 6996): 106.01470160301264, (38, 7059): 101.85405865971933, (38, 7187): 112.17405772912176, (38, 7304): 118.76705446187235, (38, 7528): 107.48850136110264, (38, 7720): 82.14249559817678, (38, 7793): 83.23592954699473, (38, 7807): 82.70290869145451, (38, 7808): 83.50526034768954, (38, 7831): 90.33268947659451, (38, 7850): 86.17575177160423, (38, 7852): 87.06760189322324, (38, 8012): 82.61419427550832, (38, 8125): 84.57120874958625, (38, 8208): 74.86798742996393, (38, 8392): 88.17049433215148, (38, 8651): 131.78661778562397, (38, 9088): 112.75814430243398, (38, 9443): 144.30583680490028, (38, 9444): 143.79461073491657, (38, 9828): 164.4988121074969, (38, 9868): 163.05690852308626, (38, 10180): 84.74242622795536, (38, 10256): 76.27975256432381, (38, 10276): 79.05834833943337, (38, 10378): 74.89506862698964, (38, 10676): 93.03656315169911, (38, 10714): 100.24281745875705, (38, 10730): 95.24650785113671, (38, 10862): 152.30757343394185, (38, 10881): 151.9287590537655, (38, 10883): 152.22757714411162, (38, 10885): 152.3263967608431, (38, 10891): 152.6982819408508, (38, 10909): 152.1184527837534, (38, 10911): 151.4362293960396, (38, 10913): 151.72684638523032, (38, 10915): 151.40666845066826, (38, 10919): 151.08132621447348, (38, 11037): 161.44309890484334, (38, 11039): 159.91213684444128, (38, 11516): 50.03001856320403, (38, 11856): 26.04684157985733, (38, 11857): 27.254953925052302, (38, 11861): 26.66010134336382, (38, 11881): 25.794453880623795, (38, 11902): 27.113816659017978, (38, 11911): 26.562875823259272, (38, 11914): 26.71369985659319, (38, 11922): 25.997389888496105, (38, 11924): 25.468675653119448, (38, 11926): 25.800463253994735, (38, 11950): 24.125051826674746, (38, 11963): 23.02080011894822, (38, 11983): 22.392642439851564, (38, 11985): 22.58211370871774, (38, 12009): 21.477140495448868, (38, 12010): 22.599223946223034, (38, 12018): 22.296365505240193, (38, 12020): 22.251577350467414, (38, 12021): 21.978278946218683, (38, 12024): 21.216950334157893, (38, 12025): 21.7368306572365, (38, 12027): 21.84797086043221, (38, 12031): 22.74657219554895, (38, 12032): 22.666040567273413, (38, 12035): 21.240073181091812, (38, 12041): 23.320244206574404, (38, 12045): 34.69017068789728, (38, 12145): 27.32875993381061, (38, 12275): 15.029135011474882, (38, 12294): 16.083857566377812, (38, 12358): 21.886172794423057, (38, 12463): 25.849251148064713, (38, 12465): 25.87115343857898, (38, 12482): 25.642549412730403, (38, 12503): 25.801957058149732, (38, 12506): 26.081228844746093, (38, 12549): 23.98405907019012, (38, 12559): 24.054952995861605, (38, 12569): 24.817272568843737, (38, 12572): 24.999719200407572, (38, 12574): 24.454899221847185, (38, 12576): 24.071328950031667, (38, 12591): 23.23048926649782, (38, 12608): 24.731488157464263, (38, 12696): 21.03083295070364, (38, 12710): 22.083819029794817, (38, 12728): 22.038398419883762, (38, 12766): 59.939291418171486, (38, 12771): 61.87757389248032, (38, 12790): 62.35884617795082, (38, 12795): 63.60778284259092, (38, 12797): 67.19610382508479, (38, 12798): 66.57910714577986, (38, 12811): 63.26198903308602, (38, 12830): 64.55743521967243, (38, 12848): 63.609971184226424, (38, 12850): 63.12498062292904, (38, 12852): 64.60108604445925, (38, 12854): 65.11251355810813, (38, 12859): 63.007385262372175, (38, 12861): 65.93343357625548, (38, 12865): 62.808371654220004, (38, 12866): 62.95401132754144, (38, 12867): 62.04072945812754, (38, 12874): 62.498794078143995, (38, 12875): 62.06379993731532, (38, 12881): 63.77600849443081, (38, 12883): 63.1336154155201, (38, 12885): 61.75692726339932, (38, 12888): 63.34851690757291, (38, 12889): 63.416940147296444, (38, 12892): 62.4353210204117, (38, 12893): 63.40513218159311, (38, 12896): 63.020445155637674, (38, 12906): 62.839892060348156, (38, 13018): 69.98639402447175, (38, 13071): 70.63639859017759, (38, 13131): 72.21906528544396, (38, 13146): 68.44089820355538, (38, 13159): 76.00958259630353, (38, 13193): 72.73613695266397, (38, 13198): 78.07835571454184, (38, 13292): 70.95497398845538, (38, 13296): 68.40138882386628, (38, 13406): 82.9079570026818, (38, 13407): 83.20096199958016, (38, 13417): 84.48286614712022, (38, 13418): 83.99036177657322, (38, 13438): 80.69010701838221, (38, 13442): 79.89293909617464, (38, 13443): 80.43285593270758, (38, 13764): 131.0627079194384, (38, 13766): 130.39333499828837, (38, 13771): 131.42522603012762, (38, 13783): 131.0112283704417, (38, 13784): 129.50204986074337, (38, 13792): 133.29799522804538, (38, 13824): 131.5431984779773, (38, 14017): 125.6463704107655, (38, 14870): 139.3607088639798, (38, 14997): 115.47202207513685, (38, 15000): 115.52063707956324, (38, 15003): 115.20682298862727, (38, 15006): 113.7504794867358, (38, 15007): 113.32521467151311, (38, 15056): 113.71560678138003, (38, 15063): 114.17160310681508, (38, 15069): 114.4514863039345, (38, 15076): 113.33286227883248, (38, 15086): 114.56684705891657, (38, 15087): 115.18456359768025, (38, 15111): 116.39194044071239, (38, 15116): 115.70829257463652, (38, 15722): 127.25623039952913, (38, 15998): 138.07120943580907, (38, 16073): 228.25387041326886, (38, 16939): 288.721664607745, (38, 16940): 288.07019802264404, (38, 16951): 288.7510246917168, (38, 16963): 288.8287554829369, (38, 16965): 289.6482984761322, (38, 16969): 289.4174646208447, (38, 16970): 289.1372761539341, (38, 16971): 288.4010913581178, (38, 16973): 288.3297769620047, (38, 16974): 289.9567775356091, (38, 16976): 289.2081069595375, (38, 16978): 288.67788897538435, (38, 16980): 289.4985612015435, (38, 16982): 289.92811785449084, (38, 17045): 310.2293347794998, (38, 17048): 311.1648349855001, (38, 17304): 12.5, (38, 17305): 12.5, (38, 17330): 12.5, (38, 17334): 12.5, (38, 17343): 12.5, (38, 17345): 12.5, (38, 17347): 12.5, (38, 17351): 12.5, (38, 17372): 12.5, (38, 17373): 12.5, (38, 17377): 12.5, (38, 17382): 12.5, (38, 17383): 12.5, (38, 17389): 12.5, (38, 17400): 12.5, (38, 17401): 12.5, (38, 17402): 12.5, (38, 17403): 12.5, (38, 17440): 12.5, (38, 17455): 12.5, (38, 17491): 12.5, (38, 17507): 12.5, (38, 17509): 12.5, (38, 17590): 12.5, (38, 17615): 12.5, (38, 17642): 12.5, (38, 17643): 12.5, (38, 17668): 12.5, (38, 17721): 14.464888173294673, (38, 17754): 12.800089004976755, (38, 17769): 12.5, (38, 17776): 12.5, (38, 17804): 12.5, (38, 17809): 12.5, (38, 17824): 12.5, (38, 17837): 12.5, (38, 17838): 12.5, (38, 17862): 12.5, (38, 17866): 12.5, (38, 17872): 12.5, (38, 17873): 12.5, (38, 17881): 12.5, (38, 17947): 235.3792133539732, (38, 17951): 234.11936128404287, (38, 17953): 233.87915265910502, (38, 17954): 233.96759064993822, (38, 17959): 235.11949022340357, (38, 17963): 234.67416059262467, (38, 18000): 228.26461306793226, (38, 18001): 228.51872857491838, (38, 18111): 246.364140400569, (38, 18148): 214.29055145979316, (38, 18166): 226.71059111402394, (38, 18189): 238.2807833340316, (38, 18239): 12.5, (38, 18240): 12.5, (38, 18245): 12.5, (38, 18247): 12.5, (38, 18251): 12.5, (38, 18256): 12.5, (38, 18258): 12.5, (38, 18259): 12.5, (38, 18260): 12.5, (38, 18262): 12.5, (38, 18263): 12.5, (38, 18264): 12.5, (38, 18266): 12.5, (38, 18267): 12.5, (38, 18268): 12.5, (38, 18269): 12.5, (38, 18275): 12.5, (38, 18285): 12.5, (38, 18308): 12.5, (38, 18313): 12.5, (38, 18314): 12.5, (38, 18315): 12.5, (38, 18316): 12.5, (38, 18317): 12.5, (38, 18320): 12.5, (38, 18321): 12.5, (38, 18322): 12.5, (38, 18324): 12.5, (38, 18325): 12.5, (38, 18326): 12.5, (38, 18327): 12.5, (38, 18329): 12.5, (38, 18330): 12.5, (38, 18331): 12.5, (38, 18332): 12.5, (38, 18333): 12.5, (38, 18336): 12.5, (38, 18337): 12.5, (38, 18403): 12.5, (38, 18432): 12.5, (38, 18451): 12.5, (38, 18466): 12.5, (38, 18481): 12.5, (38, 18483): 12.5, (38, 18484): 12.5, (38, 18485): 12.5, (38, 18486): 12.5, (38, 18487): 12.5, (38, 18489): 12.5, (38, 18490): 12.5, (38, 18491): 12.5, (38, 18492): 12.5, (38, 18493): 12.5, (38, 18494): 12.5, (38, 18495): 12.5, (38, 18496): 12.5, (38, 18497): 12.5, (38, 18498): 12.5, (38, 18499): 12.5, (38, 18501): 12.5, (38, 18502): 12.5, (38, 18503): 12.5, (38, 18504): 12.5, (38, 18506): 12.5, (38, 18507): 12.5, (38, 18508): 12.5, (38, 18509): 12.5, (38, 18510): 12.5, (38, 18511): 12.5, (38, 18512): 12.5, (38, 18515): 12.5, (38, 18516): 12.5, (38, 18517): 12.5, (38, 18518): 12.5, (38, 18519): 12.5, (38, 18520): 12.5, (38, 18522): 12.5, (38, 18523): 12.5, (38, 18532): 12.5, (38, 18535): 12.5, (38, 18537): 12.5, (38, 18539): 12.5, (38, 18540): 12.5, (38, 18541): 12.5, (38, 18542): 12.5, (38, 18543): 12.5, (38, 18546): 12.5, (38, 18555): 12.5, (38, 18556): 12.5, (38, 18565): 12.5, (38, 18567): 12.5, (38, 18568): 12.5, (38, 18577): 12.5, (38, 18583): 12.5, (38, 18605): 12.5, (38, 18608): 12.5, (38, 18616): 12.5, (38, 18618): 12.5, (38, 18625): 12.5, (38, 18645): 12.5, (38, 18646): 12.5, (38, 18653): 12.5, (38, 18654): 12.5, (38, 18655): 12.5, (38, 18666): 12.5, (38, 18837): 18.061145497111468, (38, 18974): 12.5, (38, 18999): 12.5, (38, 19000): 12.5, (38, 19174): 25.902525959852504, (38, 19342): 24.131062565947445, (38, 19455): 18.710990711899534, (38, 19555): 36.895622385987544, (38, 19564): 38.08804956421777, (38, 19573): 38.2596192120965, (38, 19586): 38.20820585922053, (38, 19605): 37.61974647338363, (38, 19611): 37.394261135558686, (38, 19614): 36.92689418955775, (38, 19641): 31.031624382007198, (38, 19702): 31.984904092427538, (38, 19713): 32.17406631378785, (38, 19731): 37.2938237995614, (38, 19819): 22.60990467533949, (38, 19893): 60.093663782299835, (38, 19899): 61.42217181376944, (38, 19929): 59.59472221479963, (38, 19951): 59.79141001951994, (38, 19962): 61.085712084386266, (38, 19970): 57.890286545817396, (38, 19971): 58.61572264033945, (38, 19972): 59.170229324804296, (38, 19975): 58.679300742463354, (38, 19978): 56.47004019708851, (38, 19987): 55.96140067561496, (38, 19989): 55.80935042441918, (38, 20039): 55.746885510013676, (38, 20043): 55.119916406355344, (38, 20047): 54.40653470131939, (38, 20052): 54.82665640024544, (38, 20054): 55.16949012131238, (38, 20085): 51.911596560995314, (38, 20104): 51.92546316033209, (38, 20132): 52.75294215212472, (38, 20203): 66.72104921377644, (38, 20280): 68.93530824720447, (38, 20285): 69.8559823219083, (38, 20290): 68.48597143822302, (38, 20297): 68.38325881261206, (38, 20309): 62.067322038046065, (38, 20453): 58.901794337902814, (38, 20485): 68.2504348785661, (38, 20520): 68.1727895727416, (38, 20526): 70.38886393965119, (38, 20698): 156.70567671877004, (38, 20868): 180.60615800551636, (38, 21042): 62.67604934844791, (38, 21057): 57.79994799227885, (38, 21066): 60.39068756648186, (38, 21075): 61.023700795308784, (38, 21093): 62.59451710827228, (38, 21098): 59.623732998678186, (38, 21127): 62.422110331474016, (38, 21130): 61.648141204274424, (38, 21144): 61.51514126572162, (38, 21146): 62.73888759541465, (38, 21147): 61.521874271379986, (38, 21148): 60.76518504016568, (38, 21153): 62.03480874686112, (38, 21293): 54.995019675608866, (38, 21426): 55.10677150590113, (38, 21442): 50.33687721948301, (38, 21451): 49.8848633645504, (38, 21466): 52.64162777453567, (38, 21469): 51.87859767089326, (38, 21471): 53.03084656743026, (38, 21473): 52.38830522323812, (38, 21475): 52.94997519474219, (38, 21482): 51.43766623811554, (38, 21484): 51.574259838057664, (38, 21488): 52.0334530795508, (38, 21494): 52.906983015187635, (38, 21498): 52.35052331938066, (38, 21500): 53.20247969059563, (38, 21514): 51.64704132782267, (38, 21537): 53.32061620054693, (38, 21662): 51.042468945217706, (38, 21691): 53.99689122560195, (38, 21757): 59.26779376785301, (38, 21777): 73.03727638000882, (38, 21778): 73.76214257032166, (38, 21779): 73.53782260342264, (38, 21790): 72.03123862195753, (38, 21802): 72.41998085342044, (38, 21824): 71.85928843591488, (38, 21874): 73.58223721976839, (38, 21879): 74.37144382818248, (38, 21983): 69.56539050853716, (38, 22002): 62.9211147075734, (38, 22132): 65.35928401073683, (38, 22261): 173.2299745447956, (38, 22298): 171.91160812694224, (38, 22339): 181.2850450108163, (38, 22508): 158.42137968527027, (38, 22841): 317.42444686896926, (38, 22842): 317.48205966049176, (38, 22874): 315.8586416626252, (38, 22941): 315.86078950025984, (38, 22956): 317.011418497629, (38, 22960): 317.2076394098965, (38, 22968): 319.0211391361915, (38, 22970): 319.22179572765907, (38, 22974): 320.20911714705494, (38, 22980): 321.54121928141393, (38, 23025): 322.02152097425903, (38, 23028): 321.84796354165087, (38, 23081): 324.8125185051795, (38, 23104): 323.352985223501, (38, 23147): 309.97442162043836, (38, 23298): 38.95156337176723, (38, 23376): 41.11477455499341, (38, 23381): 42.9419347905893, (38, 23529): 37.98366731329265, (38, 23556): 39.15680457878451, (38, 23718): 40.06029496832272, (38, 24001): 26.110340946252283, (38, 24094): 23.12822976465574, (38, 24129): 21.0153620798139, (38, 24174): 26.157381920159345, (38, 24235): 22.243022802299016, (38, 24259): 19.615690203507135, (38, 24260): 19.86448466085264, (38, 24261): 20.203097557139284, (38, 24305): 17.019127516289416, (38, 24306): 16.773278051424462, (38, 24307): 17.27577222313099, (38, 24308): 21.055815416444226, (38, 24498): 12.5, (38, 24499): 12.5, (38, 24500): 12.5, (38, 24668): 13.435048769835308, (38, 24711): 12.5, (38, 24756): 12.5, (38, 24788): 12.5, (38, 24809): 12.5, (38, 24813): 12.5, (38, 24821): 12.5, (38, 24825): 12.5, (38, 24832): 12.5, (38, 24833): 12.5, (38, 24835): 12.5, (38, 24837): 12.5, (38, 24840): 12.5, (38, 24841): 12.5, (38, 24844): 12.5, (38, 24845): 12.5, (38, 24846): 12.5, (38, 24849): 12.5, (38, 24850): 12.5, (38, 24863): 14.154488109173585, (38, 24866): 13.432310891627559, (38, 24885): 12.944561244480866, (38, 24886): 13.108228702780364, (38, 24889): 12.5, (38, 24903): 12.5, (38, 24909): 12.5, (38, 24999): 20.217515960250505, (38, 25019): 20.193727862978715, (38, 25028): 19.64379996923903, (38, 25137): 77.81020892665855, (38, 25145): 77.36466268782226, (38, 25208): 81.6170513649579, (38, 25233): 82.32359233435096, (38, 25371): 72.32956287729195, (38, 25377): 72.01785260135998, (38, 25828): 98.19512914449474, (38, 25851): 100.92924947834356, (38, 25874): 96.8009811311044, (38, 25898): 97.0720897116035, (38, 25946): 98.5499656429195, (38, 26047): 93.94902719804473, (38, 26066): 70.64240072217166, (38, 26197): 83.58018217346904, (38, 26212): 121.97943804654997, (38, 26253): 124.36439577635518, (38, 26254): 123.30015680151783, (38, 26257): 122.9657235907984, (38, 26258): 124.02967753231793, (38, 26260): 123.44498479053598, (38, 26266): 123.22764309419166, (38, 26267): 122.705735434001, (38, 26271): 122.82028229642798, (38, 26304): 113.93321648806044, (38, 26305): 113.64740819156908, (38, 26363): 102.69092719142185, (38, 26441): 177.7134856936614, (38, 26442): 177.48377208093814, (38, 26450): 176.28177364488445, (38, 26459): 176.12023901624144, (38, 26462): 176.25838546478641, (38, 26467): 179.77389312130455, (38, 26471): 178.82241004552628, (38, 26472): 178.7279595018246, (38, 26473): 178.69710687260044, (38, 26476): 178.23384704582227, (38, 26485): 176.7505755618481, (38, 26493): 176.82195236626328, (38, 26524): 176.75563633201023, (38, 26525): 176.63620430407, (38, 26556): 178.34377447861434, (38, 26560): 178.17129414387335, (38, 26561): 177.39824531652843, (38, 26564): 178.0347852403724, (38, 26569): 177.23195412360752, (38, 26570): 176.95122172671282, (38, 26573): 177.1760332493949, (38, 26581): 177.1774200216138, (38, 26583): 176.89686713470283, (38, 26593): 177.22279918897826, (38, 26837): 180.04174021812716, (38, 26844): 180.8311110223854, (38, 26863): 179.1841546590673, (38, 26893): 181.48494870126763, (38, 26902): 182.55939489961673, (38, 26905): 181.40795130831137, (38, 26912): 182.2669846352023, (38, 26921): 180.28182898914181, (38, 26922): 178.23205135348368, (38, 27212): 183.8560362337161, (38, 27218): 182.80961867097943, (38, 27239): 185.41618141683955, (38, 27257): 184.63951737687717, (38, 27274): 185.74458319617412, (38, 27279): 185.60131076350027, (38, 27282): 184.69070188577774, (38, 27283): 184.994499791106, (38, 27285): 186.1740665527215, (38, 27286): 185.38935649512499, (38, 27290): 183.9170396877436, (38, 27295): 183.31307155875461, (38, 27300): 185.8903464115415, (38, 27344): 183.58171384169407, (38, 27366): 184.64010876972785, (38, 27383): 186.3131305967206, (38, 27398): 187.3547167421738, (38, 27406): 186.42819240186918, (38, 27407): 186.67424764383705, (38, 27426): 185.28353991827785, (38, 27432): 181.4035702860533, (38, 27460): 183.806675061217, (38, 27523): 185.38005686317322, (38, 27545): 201.03549591575464, (38, 27602): 221.9545189294807, (38, 27606): 222.3009283699309, (38, 27646): 201.13859494573617, (38, 27667): 205.30034217696598, (38, 27672): 205.49837177711441, (38, 27674): 204.80150526981842, (38, 27688): 205.31566957347144, (38, 27692): 206.24127950649162, (38, 27693): 205.62251393648086, (38, 27705): 205.61268214447418, (38, 27712): 205.93616792037838, (38, 27786): 221.89274233091191, (38, 27790): 219.14553755543824, (38, 27791): 218.8885254461521, (38, 27795): 220.75442462431218, (38, 27801): 218.7469134302545, (38, 27813): 222.5800317992018, (38, 27816): 221.74191352624325, (38, 27823): 218.66706266172625, (38, 27830): 220.72974489886448, (38, 27884): 194.43677292554858, (38, 27885): 199.4277411788923, (38, 27896): 196.3984258468894, (38, 27919): 196.16797604984131, (38, 27922): 196.82249690027132, (38, 27930): 195.16673230485023, (38, 27934): 195.37794401093748, (38, 27935): 195.54197226648407, (38, 27948): 220.8440886970631, (38, 27951): 221.68793233495026, (38, 28061): 202.40638127563443, (38, 28290): 245.73785578998076, (38, 28292): 246.58282127937838, (38, 28293): 245.89919673680348, (38, 28295): 245.49758688689377, (38, 28296): 245.67819492260747, (38, 28297): 245.28499226234575, (38, 28302): 244.94618679824796, (38, 28310): 254.9858839854108, (38, 28313): 255.42983433140066, (38, 28372): 255.99317999102695, (38, 28398): 256.03065019055595, (38, 28399): 255.7163123397953, (38, 28400): 256.16900953126657, (38, 28401): 255.03580022991818, (38, 28445): 254.8683928319243, (38, 28475): 254.42807276343572, (38, 28885): 28.044489297579013, (38, 28886): 28.630738292597318, (38, 28915): 29.541099522539426, (38, 28916): 29.41139505246773, (38, 28917): 29.824586709116026, (38, 28921): 27.234824359552444, (38, 28931): 27.622896735192914, (38, 28945): 33.081466251361036, (38, 28982): 31.381560527909034, (38, 29219): 36.9928626421698, (38, 29228): 37.626620653189384, (38, 29246): 39.13586123276823, (38, 29248): 40.71605938824395, (38, 29282): 40.34510377721093, (38, 29290): 37.56124869641556, (38, 29291): 37.974264963720344, (38, 29292): 37.81366350184981, (38, 29293): 37.71339756765074, (38, 29294): 38.4597422993704, (38, 29298): 38.13468414477153, (38, 29299): 38.54820205238379, (38, 29304): 37.54934661590285, (38, 29317): 36.93952648792457, (38, 29323): 36.853318002806176, (38, 29330): 37.19020102185565, (38, 29331): 37.02624765099276, (38, 29344): 39.80048196598717, (38, 29445): 54.69197673799114, (38, 29724): 311.66298240346646, (38, 29738): 312.02290148066345, (38, 29745): 310.86615058815823, (38, 29748): 310.52948323679095, (38, 29750): 310.88728964546993, (38, 29759): 310.1030845834571, (38, 29772): 311.4243587423689, (38, 29781): 311.12020940883383, (38, 29784): 311.1276496614216, (38, 29790): 311.31175902209304, (38, 29811): 310.31684949255805, (38, 29817): 311.31673612804786, (38, 29818): 311.0107218313838, (38, 29929): 311.07721884767716, (38, 30039): 317.23691548107263, (38, 30066): 315.0374295618857, (38, 30116): 301.69032623505484, (38, 30238): 281.9790953511274, (38, 30248): 293.17696285320477, (38, 30260): 293.52582192604785, (38, 30545): 29.542083043019204, (38, 30733): 46.04617475817695, (38, 30756): 53.41710746324161, (38, 30921): 43.68772023633072, (38, 31079): 94.82705371785241, (38, 31149): 94.99954177618076, (38, 31154): 95.27577753509178, (38, 31160): 95.0927432554862, (38, 31163): 95.54690677885353, (38, 31189): 102.191872717442, (38, 31215): 102.04004104366338, (38, 31259): 104.27322145764464, (38, 31262): 104.89809457968337, (38, 31430): 95.411687328812, (38, 31568): 117.19613526269472, (38, 31751): 99.3495539195481, (41, 109): 61.23801039241796, (41, 872): 238.4591366858026, (41, 873): 239.3846809206877, (41, 877): 239.23949130611638, (41, 879): 239.39643756682204, (41, 884): 238.91892832214145, (41, 889): 239.40259911289075, (41, 891): 238.5587862423153, (41, 892): 240.07215006051948, (41, 894): 239.87260419120537, (41, 896): 238.6450328155793, (41, 903): 239.50489369405997, (41, 909): 237.26638999248516, (41, 910): 237.44887959098008, (41, 912): 236.88141906484847, (41, 913): 236.3256057184468, (41, 916): 235.8154619816355, (41, 926): 237.50530367510856, (41, 927): 237.1527033398647, (41, 948): 238.19111075496232, (41, 961): 237.9116391654716, (41, 962): 237.88559838945704, (41, 963): 237.89858027699046, (41, 967): 239.81410394721146, (41, 974): 239.78884907802475, (41, 998): 240.34624150984132, (41, 1014): 258.2411480560674, (41, 1086): 230.66881575080026, (41, 1087): 229.86511298069027, (41, 1089): 229.37825000602174, (41, 1090): 229.82171228493624, (41, 1092): 231.1473594985071, (41, 1097): 230.27183953596017, (41, 1107): 231.3727997676541, (41, 1387): 102.10707825913177, (41, 1554): 96.14298840749274, (41, 1827): 285.0753666494969, (41, 1828): 285.08870893046986, (41, 1829): 285.2908467563206, (41, 1830): 285.5463721530575, (41, 1831): 285.5584368529697, (41, 1832): 285.41866908060484, (41, 1833): 285.3606957446165, (41, 1836): 285.17476124238385, (41, 1841): 285.8765835644265, (41, 1843): 285.62518815295226, (41, 1844): 285.80579325298714, (41, 1845): 285.56686914682024, (41, 1847): 284.39493863707224, (41, 1848): 284.7535180578731, (41, 1849): 286.5024794955488, (41, 1850): 286.6146390340655, (41, 1851): 285.21207005950237, (41, 1852): 285.3973529405526, (41, 1854): 285.44284771664945, (41, 1856): 284.55563501385086, (41, 1857): 284.81633671892166, (41, 1858): 286.2285685729263, (41, 1861): 285.40614041654396, (41, 1866): 284.6710061151802, (41, 1867): 285.759097883295, (41, 1868): 285.4264596187465, (41, 1870): 285.9837430914575, (41, 1871): 285.5788647173085, (41, 1875): 285.3170330854459, (41, 1880): 284.6345166746085, (41, 1882): 284.96701420052807, (41, 1883): 286.44662694111327, (41, 1889): 284.55007727574446, (41, 1893): 285.0478651952917, (41, 1894): 284.7616254750181, (41, 1899): 284.22826211923, (41, 1900): 284.3507524830676, (41, 1902): 285.4651829445994, (41, 1905): 285.8802047200342, (41, 1907): 284.8242311412693, (41, 1910): 284.7407181853466, (41, 1917): 286.00982510664016, (41, 1920): 284.70634142578746, (41, 1935): 285.61445006303165, (41, 1937): 285.9313370954073, (41, 1946): 283.3314607229144, (41, 1949): 283.5395358118369, (41, 1950): 282.92731482547794, (41, 1951): 283.3113513054916, (41, 1952): 284.09336335151846, (41, 1953): 283.8690182708917, (41, 1954): 283.91924874310104, (41, 1958): 283.6309938016531, (41, 1960): 284.2252896563234, (41, 1968): 284.45882510934945, (41, 1969): 285.3627483001948, (41, 1974): 285.15448114619295, (41, 1975): 285.2554818727121, (41, 1979): 284.36602104732583, (41, 1980): 284.62618118902213, (41, 1981): 284.6281956712349, (41, 1985): 284.7050969616625, (41, 1994): 283.2580039295171, (41, 2011): 285.0613252640988, (41, 2019): 287.9009157812658, (41, 2020): 287.52788126226505, (41, 2029): 286.41475030047474, (41, 2030): 287.26441923795903, (41, 2032): 286.3895582534055, (41, 2033): 286.82749746164535, (41, 2034): 286.9701322401009, (41, 2036): 286.4399957731461, (41, 2037): 286.5512878633576, (41, 2038): 285.9333427432684, (41, 2042): 289.74358740628924, (41, 2050): 286.4327757433129, (41, 2051): 286.54333381428813, (41, 2053): 286.57176965883434, (41, 2054): 286.91445547415447, (41, 2066): 286.2462387183962, (41, 2067): 286.1636590731693, (41, 2071): 282.5423683001646, (41, 2072): 283.04029223467467, (41, 2073): 280.9103162288596, (41, 2074): 280.9323839663793, (41, 2080): 280.15453810961947, (41, 2082): 283.3461389439537, (41, 2083): 283.5936414570209, (41, 2089): 282.80255275057783, (41, 2090): 283.0050655663935, (41, 2092): 282.509798361569, (41, 2098): 280.33850977793566, (41, 2099): 280.7934867628973, (41, 2101): 280.4203162085915, (41, 2102): 281.89441114800564, (41, 2103): 281.490401773564, (41, 2104): 281.3387349413241, (41, 2106): 283.87151875828084, (41, 2112): 280.7528875492607, (41, 2113): 282.1946490687668, (41, 2114): 282.8041152674694, (41, 2117): 284.22345664214686, (41, 2123): 276.1089337680163, (41, 2124): 276.4119197244612, (41, 2134): 275.94964670190393, (41, 2138): 276.68083536335274, (41, 2141): 275.93133197364875, (41, 2148): 277.92392135022845, (41, 2150): 275.268394667058, (41, 2151): 275.7012233564198, (41, 2152): 275.2067387726996, (41, 2153): 277.8790790011762, (41, 2154): 276.52546522091603, (41, 2155): 276.6420078757205, (41, 2156): 276.2213298855698, (41, 2157): 277.491503501572, (41, 2160): 277.85246144561427, (41, 2161): 275.3085960643082, (41, 2162): 278.5172410087996, (41, 2163): 278.03895609208223, (41, 2164): 278.1041072954682, (41, 2168): 276.18694024742473, (41, 2172): 277.1795900269125, (41, 2174): 275.85995832045563, (41, 2178): 277.63635628010195, (41, 2179): 277.4984937098448, (41, 2183): 276.83996572014826, (41, 2185): 276.95510517021734, (41, 2186): 276.6621486541018, (41, 2190): 277.7423966767938, (41, 2192): 277.2480243189753, (41, 2193): 276.8712488620024, (41, 2194): 276.366980996492, (41, 2195): 276.5001169388643, (41, 2197): 277.4568556311841, (41, 2205): 277.0418386141771, (41, 2207): 276.4372201687332, (41, 2208): 276.8163056299142, (41, 2212): 276.5664006826753, (41, 2214): 270.1021249507679, (41, 2225): 271.82834756249053, (41, 2231): 265.196484461617, (41, 2278): 277.93257907956894, (41, 2284): 279.2573757862434, (41, 2285): 279.25055065236035, (41, 2291): 278.15107112216083, (41, 2292): 277.3041974588766, (41, 2307): 278.6346423282292, (41, 2313): 278.2474813155436, (41, 2317): 276.1353340464025, (41, 2319): 277.75295156178424, (41, 2321): 278.38791630443376, (41, 2323): 278.0279141068019, (41, 2326): 279.22208613419707, (41, 2327): 278.78679681363167, (41, 2329): 278.52069630193444, (41, 2330): 278.28837183521074, (41, 2332): 279.1459912308578, (41, 2344): 277.6046743874791, (41, 2346): 277.79401464414974, (41, 2361): 275.86782864987896, (41, 2368): 281.9618934846826, (41, 2374): 282.604426606825, (41, 2375): 282.6607820353008, (41, 2377): 280.8227353189241, (41, 2378): 283.0544439417292, (41, 2379): 283.30750985756316, (41, 2380): 283.32521020219724, (41, 2383): 281.14481042912536, (41, 2385): 281.3320963820609, (41, 2395): 281.17388352119025, (41, 2397): 283.20122514027565, (41, 2398): 280.2606002648748, (41, 2399): 280.7744487830804, (41, 2400): 280.63292009082863, (41, 2402): 282.1927701378481, (41, 2403): 282.5881758915291, (41, 2404): 282.60399492801196, (41, 2405): 281.7285309475782, (41, 2407): 282.3169065868453, (41, 2408): 282.87014757230867, (41, 2409): 281.9612237546542, (41, 2411): 282.93407666580225, (41, 2412): 282.69963684147837, (41, 2413): 283.071770216343, (41, 2414): 282.592040385741, (41, 2422): 282.9353124083654, (41, 2424): 282.7346781183822, (41, 2426): 282.74928834632897, (41, 2433): 282.1521363285616, (41, 2436): 282.18555551439516, (41, 2437): 279.82880749654066, (41, 2440): 280.2857989538425, (41, 2445): 292.27871518557686, (41, 2447): 290.8400694827584, (41, 2454): 292.0048714388675, (41, 2455): 291.9055562734186, (41, 2460): 288.50843085425464, (41, 2461): 288.9634738011763, (41, 2471): 297.06694646684986, (41, 2492): 295.7109695255796, (41, 2511): 291.13247127018536, (41, 2523): 293.49729032293527, (41, 2525): 293.2963136876846, (41, 2535): 290.93939452899224, (41, 2537): 290.2594290042074, (41, 2538): 290.5694138324975, (41, 2539): 291.12658587128027, (41, 2540): 291.2679555003413, (41, 2542): 292.0348337914788, (41, 2559): 301.25491033877347, (41, 2575): 301.21081125151045, (41, 2599): 282.58842440618076, (41, 2600): 286.7873201536384, (41, 2607): 283.7470967079384, (41, 2627): 296.02320865179104, (41, 2647): 298.5928231953591, (41, 2674): 296.7151463983298, (41, 2681): 296.82927857448567, (41, 2683): 297.6513656296141, (41, 2686): 296.30690509557456, (41, 2689): 310.0603620271215, (41, 2690): 310.2214868630242, (41, 2713): 315.6583727329915, (41, 2714): 316.26719217717306, (41, 2715): 316.5777758457937, (41, 2739): 316.1893946290705, (41, 2740): 313.1580278160165, (41, 2741): 313.236551874733, (41, 2749): 316.16277672376634, (41, 2750): 316.12455426813625, (41, 2752): 316.28481602236775, (41, 2755): 316.6169347523567, (41, 2758): 316.6590983014101, (41, 2759): 316.59919374146955, (41, 2769): 316.0822101237492, (41, 2771): 313.9407867898455, (41, 2779): 315.0307445634222, (41, 2784): 311.9245940449827, (41, 2800): 313.52681408803994, (41, 2802): 313.08284920973676, (41, 2803): 312.8388439272719, (41, 2804): 312.57943320594774, (41, 2805): 313.72303731699213, (41, 2807): 313.5776083728896, (41, 2809): 313.74106146175114, (41, 2812): 311.4021828971796, (41, 2814): 314.4632649572514, (41, 2817): 315.6445936829584, (41, 2819): 313.31037374708256, (41, 2823): 312.68159511691715, (41, 2832): 314.2922916038956, (41, 2836): 312.85488265305327, (41, 2839): 313.4453922787114, (41, 2841): 315.152499741921, (41, 2843): 314.8470516090711, (41, 2846): 313.643888389665, (41, 2849): 314.72806114486934, (41, 2852): 314.32146892833674, (41, 2853): 314.92291523112294, (41, 2876): 315.6502990562767, (41, 2877): 316.8892122662031, (41, 2885): 318.4146915275059, (41, 2918): 312.6646428841, (41, 2921): 313.3135454069219, (41, 2925): 309.85513283712106, (41, 2926): 308.46129437474195, (41, 2930): 312.25544614872456, (41, 2931): 310.4219920608107, (41, 2938): 312.89134344235947, (41, 2940): 313.2998210865383, (41, 2947): 311.3149279738734, (41, 2949): 311.7421532182589, (41, 2950): 312.18355329469296, (41, 2952): 311.94314427859115, (41, 2958): 311.805723052151, (41, 2959): 311.7922568236783, (41, 2960): 312.4263105853921, (41, 2961): 312.26172197962666, (41, 2963): 311.72232277750084, (41, 2968): 312.0082200879106, (41, 2976): 311.5249810948061, (41, 2981): 308.4181770215561, (41, 2982): 308.5414295334659, (41, 2984): 308.3603456382343, (41, 3003): 308.22209426338924, (41, 3046): 302.1333492190687, (41, 3050): 306.0063319442823, (41, 3051): 306.0977711182113, (41, 3053): 305.6768753291278, (41, 3069): 309.0633318496747, (41, 3071): 304.9579214803418, (41, 3080): 318.8436625135128, (41, 3199): 308.99572073032346, (41, 3200): 308.6159148396675, (41, 3205): 311.86691398575755, (41, 3209): 308.932261577639, (41, 3215): 308.50990812390665, (41, 3217): 307.87091094190555, (41, 3249): 308.42060617743056, (41, 3263): 313.1870008739926, (41, 3289): 309.54764301455845, (41, 3301): 310.06675782361896, (41, 3302): 309.70182837774655, (41, 3307): 309.3760285980574, (41, 3310): 310.342410155144, (41, 3391): 317.7764881409042, (41, 3509): 200.15599817047226, (41, 3510): 199.7079923085883, (41, 3511): 199.8045802001285, (41, 3512): 199.3505924051441, (41, 3514): 199.28449191118443, (41, 3519): 202.19039430096592, (41, 3536): 200.59178135222797, (41, 3545): 201.0917883668735, (41, 3548): 200.13930028603406, (41, 3572): 201.09151777750193, (41, 3581): 201.21903078303836, (41, 3583): 200.08530823841704, (41, 3601): 203.3434698631607, (41, 3656): 203.3784325506413, (41, 3669): 204.14088771598955, (41, 3670): 204.612686679623, (41, 3695): 201.63143932614852, (41, 3696): 201.9198705686905, (41, 3782): 196.75848765922498, (41, 3792): 196.81090168998085, (41, 3989): 132.8559046183579, (41, 4008): 135.00016898277244, (41, 4031): 136.46967533728193, (41, 4045): 134.17260235361138, (41, 4144): 132.76888198504602, (41, 4145): 128.9589117342519, (41, 4164): 131.54911501438121, (41, 4168): 130.10472538537297, (41, 4173): 129.57953104034635, (41, 4181): 128.29546526719065, (41, 4228): 128.85722771482153, (41, 4248): 125.94861915656841, (41, 4254): 107.5275466820551, (41, 4260): 108.40235535049419, (41, 4262): 108.5216814839142, (41, 4273): 108.91309349343632, (41, 4319): 98.41812770058567, (41, 4326): 98.41986429588093, (41, 4328): 98.73625318118818, (41, 4334): 98.43160347891074, (41, 4335): 98.12703638850371, (41, 4372): 14.940180354184312, (41, 4413): 12.5, (41, 4434): 15.679102952587137, (41, 4447): 16.227212860489196, (41, 4452): 15.367650409838332, (41, 4463): 28.846093590881466, (41, 4465): 28.267696320968856, (41, 4619): 12.5, (41, 4645): 12.5, (41, 4657): 12.5, (41, 4666): 12.5, (41, 4676): 12.5, (41, 4678): 12.5, (41, 4689): 12.5, (41, 4704): 12.5, (41, 4726): 25.812261543775886, (41, 4727): 25.471834154500563, (41, 4730): 24.787051477403075, (41, 4731): 25.146875212617623, (41, 4734): 24.63428207296946, (41, 4735): 24.438110164458845, (41, 4736): 24.711281114018604, (41, 4737): 24.294369569812165, (41, 4738): 24.464046438874337, (41, 4756): 24.876025477712254, (41, 4760): 22.547635663303964, (41, 4761): 22.51068174392448, (41, 4762): 22.22876991337989, (41, 4765): 22.785000230094084, (41, 4773): 26.348031642052, (41, 4774): 26.26266939506474, (41, 4790): 26.08996333657942, (41, 4795): 25.739729921378558, (41, 4799): 26.52799040271211, (41, 4801): 27.554550541588757, (41, 4804): 25.595918366574704, (41, 4805): 25.313711516595905, (41, 4806): 26.467097890350225, (41, 4815): 26.346766685708783, (41, 4816): 27.0922557200809, (41, 4817): 27.533927465976532, (41, 4826): 26.941515490254734, (41, 4830): 26.5762783835838, (41, 4839): 23.54392261273612, (41, 4840): 23.9407293496955, (41, 4841): 23.30530452222025, (41, 4846): 23.032528532367404, (41, 4848): 23.152667803514255, (41, 4850): 23.49530421328907, (41, 4871): 18.76538557544895, (41, 4883): 21.906317213961948, (41, 4900): 20.06701303030084, (41, 4901): 19.772030922190915, (41, 4917): 12.5, (41, 4931): 12.5, (41, 4944): 12.5, (41, 4956): 12.5, (41, 4958): 12.5, (41, 4959): 12.5, (41, 4961): 12.5, (41, 4966): 12.5, (41, 5207): 12.5, (41, 5272): 54.78665273184437, (41, 5283): 53.85386868560936, (41, 5287): 51.5597883810936, (41, 5289): 51.123080993764916, (41, 5293): 55.455856012285615, (41, 5295): 52.9684342838272, (41, 5296): 52.45827604940566, (41, 5298): 52.200400495780855, (41, 5303): 51.03548208307148, (41, 5305): 54.340091771345115, (41, 5306): 54.3686031842545, (41, 5307): 54.76239680594432, (41, 5308): 53.77388685285929, (41, 5313): 54.42414320558721, (41, 5314): 54.04947297722949, (41, 5317): 53.46174134247455, (41, 5319): 51.77215090372094, (41, 5324): 52.65600653596615, (41, 5326): 53.25996589604838, (41, 5348): 54.187252676637186, (41, 5351): 52.92415594041223, (41, 5399): 49.94181228285093, (41, 5413): 50.91412264421872, (41, 5422): 49.91998747112266, (41, 5445): 51.73603666070344, (41, 5448): 52.57136006115374, (41, 5456): 52.28656846993452, (41, 5467): 51.38588264246428, (41, 5624): 62.17546762549499, (41, 5671): 43.83598885234607, (41, 5672): 45.00889815358307, (41, 5797): 30.850065215909833, (41, 5871): 35.06527417136005, (41, 5976): 44.56655422079149, (41, 6118): 269.8098331027092, (41, 6248): 284.4648416842644, (41, 6345): 130.70886670342958, (41, 6352): 132.6654549873744, (41, 6354): 129.9837773402425, (41, 6359): 130.04322665354255, (41, 6376): 133.43257923409027, (41, 6378): 130.2654836525647, (41, 6381): 130.5110830823509, (41, 6383): 130.94569719969567, (41, 6396): 132.49218322532602, (41, 6399): 131.2189998960418, (41, 6408): 132.15362995295555, (41, 6409): 130.0644607910391, (41, 6419): 131.44152319456762, (41, 6422): 130.9793861948275, (41, 6423): 131.07325348425147, (41, 6424): 128.8567033147049, (41, 6439): 128.8531831359495, (41, 6464): 129.0292474860247, (41, 6465): 129.6260014264969, (41, 6469): 130.23095948140667, (41, 6470): 130.54653614237685, (41, 6472): 129.56060172996152, (41, 6480): 128.00397709875458, (41, 6486): 124.76730281968307, (41, 6497): 125.75346498450615, (41, 6503): 126.54012232926519, (41, 6508): 127.67957206590242, (41, 6509): 126.7190070054761, (41, 6521): 126.8807743011927, (41, 6544): 125.78044231968055, (41, 6552): 128.56319027674652, (41, 6553): 128.74010780371, (41, 6554): 128.9371220973326, (41, 6578): 128.44735011013944, (41, 6582): 127.32825727040981, (41, 6601): 128.09349226040226, (41, 6609): 127.76280832381586, (41, 6610): 127.42948827130417, (41, 6611): 128.0943033357374, (41, 6614): 128.62703600247858, (41, 6615): 128.34150793971654, (41, 6616): 127.19936136555437, (41, 6617): 127.62133992966992, (41, 6618): 126.3717156560415, (41, 6619): 128.64101879448626, (41, 6620): 126.754493958602, (41, 6621): 126.84930769318439, (41, 6622): 127.11072456695558, (41, 6623): 128.16812857654466, (41, 6624): 127.87321586982605, (41, 6625): 128.1443956651119, (41, 6626): 128.84268199513932, (41, 6627): 129.05536640883182, (41, 6628): 126.34412032463612, (41, 6629): 127.28279845055188, (41, 6630): 129.00547122148316, (41, 6632): 127.54560269159462, (41, 6634): 128.92557115540765, (41, 6635): 127.15352927464016, (41, 6636): 127.03653264468002, (41, 6637): 127.48958510350418, (41, 6638): 128.56627556081222, (41, 6639): 128.78057299283185, (41, 6640): 128.75652844909388, (41, 6641): 126.50949906097765, (41, 6642): 128.27035284512803, (41, 6643): 129.17549687784557, (41, 6645): 128.41593990143141, (41, 6646): 126.78523972773478, (41, 6647): 128.37645005498072, (41, 6653): 128.4849944050825, (41, 6655): 128.92088034593405, (41, 6658): 128.76852955971276, (41, 6662): 127.96777362957876, (41, 6819): 133.79729922050205, (41, 6996): 123.54017929287505, (41, 7059): 120.98684190668784, (41, 7187): 112.22398232219275, (41, 7304): 125.96558184861243, (41, 7528): 117.887332402142, (41, 7720): 108.56315266973834, (41, 7793): 106.30086729885343, (41, 7807): 106.9483998606399, (41, 7808): 105.7833991344446, (41, 7831): 123.40251606780514, (41, 7850): 123.51399347204884, (41, 7852): 124.6124771138663, (41, 8012): 112.68899839522437, (41, 8125): 93.61462736005213, (41, 8208): 104.48204048847033, (41, 8392): 114.75277878237179, (41, 8651): 146.8798943482768, (41, 9088): 142.58842485334802, (41, 9443): 136.51401028343568, (41, 9444): 135.7868627862557, (41, 9828): 145.49917063565584, (41, 9868): 151.82113899594503, (41, 10180): 92.26824116976539, (41, 10256): 85.49866570252013, (41, 10276): 90.57335317582395, (41, 10378): 96.71080820725139, (41, 10676): 85.04500950294383, (41, 10714): 87.63353474364455, (41, 10730): 93.24635999249655, (41, 10862): 70.311162031002, (41, 10881): 68.76142084357865, (41, 10883): 69.04948273577183, (41, 10885): 70.61675286364924, (41, 10891): 69.49870001201755, (41, 10909): 69.35606379770704, (41, 10911): 68.85832356767929, (41, 10913): 69.30667570911942, (41, 10915): 69.18034170981339, (41, 10919): 68.84490684784892, (41, 11037): 82.67218742163715, (41, 11039): 85.36217842190261, (41, 11516): 171.18562681852944, (41, 11856): 98.4818700515539, (41, 11857): 97.17014822218042, (41, 11861): 97.80294085371749, (41, 11881): 99.25113129927377, (41, 11902): 98.86767583162637, (41, 11911): 99.98438258847705, (41, 11914): 99.51909153278555, (41, 11922): 99.3893676573101, (41, 11924): 99.78701711545183, (41, 11926): 99.74342608075689, (41, 11950): 101.27042414260615, (41, 11963): 101.48515575362025, (41, 11983): 103.35205225744862, (41, 11985): 101.4960581225716, (41, 12009): 103.22621645229694, (41, 12010): 102.61310859929497, (41, 12018): 102.88322962214305, (41, 12020): 102.67289470514696, (41, 12021): 102.89988904016121, (41, 12024): 103.08313248621705, (41, 12025): 102.65384436346228, (41, 12027): 102.70094406876895, (41, 12031): 102.57344329307051, (41, 12032): 102.34884315363381, (41, 12035): 103.62655343684628, (41, 12041): 100.46522423721497, (41, 12045): 100.84323863919973, (41, 12145): 103.10200370330479, (41, 12275): 137.0630824926896, (41, 12294): 137.90218762289106, (41, 12358): 143.39687437965074, (41, 12463): 146.90964319336905, (41, 12465): 146.9771505068837, (41, 12482): 145.95294099877532, (41, 12503): 146.28576535408178, (41, 12506): 146.42879225642014, (41, 12549): 144.09320802222834, (41, 12559): 144.39194741063548, (41, 12569): 145.2264264629583, (41, 12572): 145.2911627202492, (41, 12574): 144.9327889513751, (41, 12576): 143.9695560637909, (41, 12591): 142.77299401710988, (41, 12608): 142.74199776418828, (41, 12696): 140.65662987461593, (41, 12710): 139.8418927637511, (41, 12728): 141.15071802157044, (41, 12766): 129.69308192798343, (41, 12771): 125.63961273297146, (41, 12790): 125.80354371278696, (41, 12795): 126.69825439174913, (41, 12797): 124.30486674144143, (41, 12798): 124.12701560730248, (41, 12811): 124.32212105165141, (41, 12830): 125.02146762594317, (41, 12848): 123.48444642991242, (41, 12850): 122.55251407539826, (41, 12852): 124.54365746872554, (41, 12854): 124.52811442592734, (41, 12859): 123.08976507754227, (41, 12861): 123.78722440576408, (41, 12865): 125.04434313071287, (41, 12866): 124.56815473883526, (41, 12867): 125.03823512494752, (41, 12874): 124.87361672500631, (41, 12875): 124.6953119067597, (41, 12881): 125.15125317674814, (41, 12883): 125.125032846582, (41, 12885): 124.81974192453306, (41, 12888): 124.80699902257054, (41, 12889): 124.49897380123898, (41, 12892): 125.05752659887291, (41, 12893): 125.12580359053268, (41, 12896): 124.81580800819276, (41, 12906): 126.28882629687514, (41, 13018): 134.44680377299002, (41, 13071): 136.26011223404473, (41, 13131): 129.2514093088147, (41, 13146): 127.51819568821615, (41, 13159): 137.17908037781694, (41, 13193): 128.77673684111625, (41, 13198): 126.51404999315363, (41, 13292): 124.7731972418991, (41, 13296): 121.33147994113982, (41, 13406): 132.11960582528923, (41, 13407): 132.55061542854665, (41, 13417): 135.75133225559432, (41, 13418): 136.13624615508442, (41, 13438): 133.2079606924239, (41, 13442): 132.06863798331753, (41, 13443): 132.29464514199435, (41, 13764): 169.29921192336423, (41, 13766): 168.93514853801054, (41, 13771): 170.31764043135516, (41, 13783): 167.8914818071662, (41, 13784): 168.09500606429026, (41, 13792): 172.561452373129, (41, 13824): 168.34975102036682, (41, 14017): 160.20050489116636, (41, 14870): 66.00232937765976, (41, 14997): 113.4020489245117, (41, 15000): 112.83537225385373, (41, 15003): 111.99707965043959, (41, 15006): 113.60782423504764, (41, 15007): 113.23883802203251, (41, 15056): 111.69535174595913, (41, 15063): 111.67011175256641, (41, 15069): 111.18037448358723, (41, 15076): 112.81347499139322, (41, 15086): 114.48066295442618, (41, 15087): 114.08706904076759, (41, 15111): 115.57055607829749, (41, 15116): 114.66497611253398, (41, 15722): 123.84690445592061, (41, 15998): 118.36730484992344, (41, 16073): 246.13919742837425, (41, 16939): 262.4575128051349, (41, 16940): 261.7489755135753, (41, 16951): 263.1141819338393, (41, 16963): 263.0444009306727, (41, 16965): 263.66095532756975, (41, 16969): 263.8024620750846, (41, 16970): 263.15902979764587, (41, 16971): 262.5832601986339, (41, 16973): 262.74573202066716, (41, 16974): 264.1016745202654, (41, 16976): 263.0762182133389, (41, 16978): 262.5850111923202, (41, 16980): 263.1175366013401, (41, 16982): 264.3068720351758, (41, 17045): 298.9984181982571, (41, 17048): 299.88192102719466, (41, 17304): 120.98664354893243, (41, 17305): 121.89364928392393, (41, 17330): 121.7580846282666, (41, 17334): 120.33124378893652, (41, 17343): 122.32775194536727, (41, 17345): 121.50989880348818, (41, 17347): 122.5025219219253, (41, 17351): 119.72644125633293, (41, 17372): 120.73404770082016, (41, 17373): 122.11919251624661, (41, 17377): 122.31443340845351, (41, 17382): 121.66257665461794, (41, 17383): 121.38365653252313, (41, 17389): 121.09785436450335, (41, 17400): 121.56321195855864, (41, 17401): 121.36090102986756, (41, 17402): 121.7168379067042, (41, 17403): 121.87858383484875, (41, 17440): 122.83715029402116, (41, 17455): 122.99745379835619, (41, 17491): 123.9349503890193, (41, 17507): 117.16535312648283, (41, 17509): 117.1687601877988, (41, 17590): 120.85376478369301, (41, 17615): 111.41370378076675, (41, 17642): 112.32501926276784, (41, 17643): 112.77061462448727, (41, 17668): 111.10496110338433, (41, 17721): 107.73992114294994, (41, 17754): 109.74106264494696, (41, 17769): 115.88492648326508, (41, 17776): 116.8989063316651, (41, 17804): 116.16453330007221, (41, 17809): 116.46862857446088, (41, 17824): 115.49959433389775, (41, 17837): 118.21878314984912, (41, 17838): 118.93040619406761, (41, 17862): 119.03436102662582, (41, 17866): 119.34489049199404, (41, 17872): 118.41180234817085, (41, 17873): 118.3373571688536, (41, 17881): 118.5550075865287, (41, 17947): 200.8465528450579, (41, 17951): 200.0912754335141, (41, 17953): 199.72344067617826, (41, 17954): 199.62966994914862, (41, 17959): 201.075345430685, (41, 17963): 201.19719943908424, (41, 18000): 196.744331004075, (41, 18001): 196.59769293070312, (41, 18111): 198.93054929940698, (41, 18148): 174.84802020596803, (41, 18166): 182.70463053659006, (41, 18189): 192.86942110868395, (41, 18239): 121.8253595899841, (41, 18240): 121.95424079385963, (41, 18245): 121.92302862494502, (41, 18247): 121.99621296138332, (41, 18251): 122.08316893576631, (41, 18256): 122.33183478226934, (41, 18258): 122.33015794474655, (41, 18259): 122.41551561597136, (41, 18260): 122.54552021653542, (41, 18262): 122.69523949509264, (41, 18263): 122.42775055787882, (41, 18264): 122.54866378922668, (41, 18266): 122.83615451098544, (41, 18267): 122.93572534560018, (41, 18268): 123.03402652544348, (41, 18269): 123.24649071596943, (41, 18275): 123.1468521398959, (41, 18285): 122.45534045380572, (41, 18308): 120.22467044991586, (41, 18313): 119.8441940800461, (41, 18314): 120.43337890305463, (41, 18315): 122.87034201834959, (41, 18316): 123.03411343930502, (41, 18317): 123.14467649772416, (41, 18320): 122.99255683921636, (41, 18321): 123.13322685685648, (41, 18322): 123.2715091951115, (41, 18324): 123.1319256860134, (41, 18325): 123.3167128523782, (41, 18326): 123.23968753372493, (41, 18327): 123.39369021838858, (41, 18329): 123.20228848186778, (41, 18330): 123.65964465172853, (41, 18331): 123.44915651685508, (41, 18332): 123.32369589952901, (41, 18333): 123.48330540123821, (41, 18336): 123.11519800716069, (41, 18337): 123.06503269734812, (41, 18403): 123.96395985979954, (41, 18432): 126.56125388315523, (41, 18451): 124.8341027596173, (41, 18466): 122.6410482456875, (41, 18481): 122.44863850364506, (41, 18483): 122.57401615911799, (41, 18484): 122.37637115471762, (41, 18485): 121.653594949937, (41, 18486): 121.47493877199283, (41, 18487): 121.08552104107518, (41, 18489): 121.87493642479994, (41, 18490): 121.76796388591526, (41, 18491): 121.8791059955229, (41, 18492): 120.95560885456474, (41, 18493): 121.28430345445153, (41, 18494): 121.932087768334, (41, 18495): 121.66625066483859, (41, 18496): 121.65382798120449, (41, 18497): 120.87842077210063, (41, 18498): 121.44873261929544, (41, 18499): 121.66876452261494, (41, 18501): 121.28558517532751, (41, 18502): 121.13023934292345, (41, 18503): 121.16565198032242, (41, 18504): 121.8557287513708, (41, 18506): 120.94159084064651, (41, 18507): 120.72090189011735, (41, 18508): 121.51522967155528, (41, 18509): 121.39778562416956, (41, 18510): 120.99182612951698, (41, 18511): 121.0674810127817, (41, 18512): 121.1435406635249, (41, 18515): 121.68923319806865, (41, 18516): 121.28325457804067, (41, 18517): 120.90455659896753, (41, 18518): 121.50995749014366, (41, 18519): 121.95874577030084, (41, 18520): 121.62536546326352, (41, 18522): 122.78751690270327, (41, 18523): 122.67705690449048, (41, 18532): 122.6595820265861, (41, 18535): 122.5546399247159, (41, 18537): 122.49663402774405, (41, 18539): 122.43674986091516, (41, 18540): 122.36734122543386, (41, 18541): 122.33291042486525, (41, 18542): 122.32421645335717, (41, 18543): 122.3112615494455, (41, 18546): 122.08284488270691, (41, 18555): 122.16101204953694, (41, 18556): 122.08110090858749, (41, 18565): 122.46692692445762, (41, 18567): 122.21884726478024, (41, 18568): 122.29171025021559, (41, 18577): 122.6670986453775, (41, 18583): 122.98357654580438, (41, 18605): 123.52003467874272, (41, 18608): 121.69576055752393, (41, 18616): 123.85624677642288, (41, 18618): 123.90857879756203, (41, 18625): 124.81560927127141, (41, 18645): 124.9594821104319, (41, 18646): 124.6982132325374, (41, 18653): 123.4850523570359, (41, 18654): 123.6835483345508, (41, 18655): 123.3449609959523, (41, 18666): 126.04732698455072, (41, 18837): 139.13618902067583, (41, 18974): 127.95478942385199, (41, 18999): 129.86189894298792, (41, 19000): 129.9916035175507, (41, 19174): 133.47739046821607, (41, 19342): 138.23384096083402, (41, 19455): 127.8155051028701, (41, 19555): 128.50676668829578, (41, 19564): 132.4637506722702, (41, 19573): 131.51968029703067, (41, 19586): 130.85480697223127, (41, 19605): 130.30222824344173, (41, 19611): 130.79570718398958, (41, 19614): 129.5413097798907, (41, 19641): 133.428835026203, (41, 19702): 134.5405654735965, (41, 19713): 133.9951027743866, (41, 19731): 122.4353659728334, (41, 19819): 129.52929085916384, (41, 19893): 68.73566333157059, (41, 19899): 64.77920302780957, (41, 19929): 68.57296507649924, (41, 19951): 64.2164252281689, (41, 19962): 66.49647701525168, (41, 19970): 68.94851895332482, (41, 19971): 68.12616529931547, (41, 19972): 67.91584517987532, (41, 19975): 68.65371936673729, (41, 19978): 67.11094694867347, (41, 19987): 67.59956401816291, (41, 19989): 68.57881269076015, (41, 20039): 67.69372274920104, (41, 20043): 68.07196623846482, (41, 20047): 69.03172560882118, (41, 20052): 69.46925369504754, (41, 20054): 69.02650093970384, (41, 20085): 70.15613229220126, (41, 20104): 70.14456044641987, (41, 20132): 69.55681347347695, (41, 20203): 61.76582896673615, (41, 20280): 60.01712286266432, (41, 20285): 59.20219507798159, (41, 20290): 60.23184899232829, (41, 20297): 60.852057327910124, (41, 20309): 61.11891094707479, (41, 20453): 63.33315117645987, (41, 20485): 64.6350986889187, (41, 20520): 66.39587214995781, (41, 20526): 64.59968119711047, (41, 20698): 196.4784654613325, (41, 20868): 212.7444822681405, (41, 21042): 103.79828735340952, (41, 21057): 104.02976409003368, (41, 21066): 102.88255136136995, (41, 21075): 104.29175755501687, (41, 21093): 102.41901179433185, (41, 21098): 100.48207434150443, (41, 21127): 103.06869048175352, (41, 21130): 102.40663319873408, (41, 21144): 103.71667737579438, (41, 21146): 103.07100780583751, (41, 21147): 104.10792998169268, (41, 21148): 103.66860003723038, (41, 21153): 108.73245528943619, (41, 21293): 102.3799501110615, (41, 21426): 115.10319101089247, (41, 21442): 118.12905347172358, (41, 21451): 118.37620932566416, (41, 21466): 115.89805597843252, (41, 21469): 115.72255227205187, (41, 21471): 116.01625630401179, (41, 21473): 115.71428637155199, (41, 21475): 115.81322849232527, (41, 21482): 116.13027668590236, (41, 21484): 115.89364594468886, (41, 21488): 116.13513521135646, (41, 21494): 115.09863178174598, (41, 21498): 115.14776832518801, (41, 21500): 114.50641328869803, (41, 21514): 111.79854031920887, (41, 21537): 112.91745437215721, (41, 21662): 109.89093760036634, (41, 21691): 110.00606341384577, (41, 21757): 115.70800640645422, (41, 21777): 100.10695687995549, (41, 21778): 100.30566075755354, (41, 21779): 99.56860678997488, (41, 21790): 100.5707764207955, (41, 21802): 99.34912522682671, (41, 21824): 98.52559977638896, (41, 21874): 98.74882773352248, (41, 21879): 97.72560653111195, (41, 21983): 103.3045883536498, (41, 22002): 97.40111973654614, (41, 22132): 113.26447137724287, (41, 22261): 138.798203481974, (41, 22298): 136.6747444322246, (41, 22339): 141.0950284891177, (41, 22508): 128.15659551687435, (41, 22841): 328.7061060920237, (41, 22842): 328.60599565223276, (41, 22874): 326.52375587075517, (41, 22941): 327.0543267848115, (41, 22956): 328.01904855075674, (41, 22960): 328.57867395153676, (41, 22968): 328.1838153073453, (41, 22970): 328.6818798112536, (41, 22974): 328.2806878324522, (41, 22980): 329.53431089701616, (41, 23025): 328.0544364192207, (41, 23028): 327.4912273250028, (41, 23081): 327.8673913548922, (41, 23104): 323.1608347682445, (41, 23147): 316.15216990353224, (41, 23298): 108.53614362574052, (41, 23376): 108.06309804542576, (41, 23381): 104.58896492038123, (41, 23529): 106.20959032391117, (41, 23556): 106.3368011092682, (41, 23718): 110.91116919307082, (41, 24001): 112.8395339869675, (41, 24094): 108.70575781725307, (41, 24129): 109.49903503286072, (41, 24174): 105.68138320086096, (41, 24235): 105.91205797505076, (41, 24259): 108.16244696019015, (41, 24260): 107.87945990869467, (41, 24261): 107.91159336341268, (41, 24305): 109.75416550418777, (41, 24306): 109.62813162131611, (41, 24307): 109.54428521295594, (41, 24308): 118.37967208481264, (41, 24498): 116.44872819937757, (41, 24499): 116.36560281801015, (41, 24500): 116.30167459504091, (41, 24668): 120.6510189455176, (41, 24711): 115.2652640436691, (41, 24756): 113.98010455462882, (41, 24788): 115.0802798657931, (41, 24809): 112.04667132769914, (41, 24813): 113.1550437793665, (41, 24821): 112.86578773844808, (41, 24825): 112.75585547266338, (41, 24832): 112.10154905152844, (41, 24833): 112.37547590465377, (41, 24835): 112.55089688158323, (41, 24837): 113.22017937227588, (41, 24840): 111.94057967928894, (41, 24841): 112.60951226472527, (41, 24844): 111.79228691388079, (41, 24845): 112.6689465302285, (41, 24846): 111.76219128304349, (41, 24849): 111.83472197252746, (41, 24850): 113.04365441154937, (41, 24863): 110.45654618120042, (41, 24866): 110.98748512980652, (41, 24885): 111.01486741702217, (41, 24886): 110.70737436161225, (41, 24889): 113.0157009698709, (41, 24903): 113.9753869783089, (41, 24909): 113.05278438725591, (41, 24999): 139.82787512843794, (41, 25019): 140.38698876588967, (41, 25028): 139.21386210474748, (41, 25137): 49.86521493583629, (41, 25145): 49.83074868223397, (41, 25208): 41.48367299937674, (41, 25233): 41.10161462375565, (41, 25371): 55.46412254562164, (41, 25377): 57.307446172335204, (41, 25828): 78.09290564667552, (41, 25851): 85.05791871986762, (41, 25874): 80.10400215331829, (41, 25898): 75.68798458407332, (41, 25946): 78.69671298197808, (41, 26047): 64.80470017634492, (41, 26066): 72.30484208046771, (41, 26197): 68.79353270348345, (41, 26212): 86.93790729662348, (41, 26253): 88.16106276757277, (41, 26254): 87.84646567145762, (41, 26257): 86.91043534586828, (41, 26258): 87.76564364198566, (41, 26260): 87.36260241788091, (41, 26266): 88.99495862783023, (41, 26267): 88.34375577552538, (41, 26271): 88.18163684800201, (41, 26304): 84.8551978182597, (41, 26305): 85.32531537818244, (41, 26363): 76.57978728934374, (41, 26441): 125.75725635805944, (41, 26442): 125.82256797882738, (41, 26450): 124.8545688202647, (41, 26459): 123.71789337026797, (41, 26462): 123.38298168959038, (41, 26467): 126.05902749605909, (41, 26471): 125.8378105160669, (41, 26472): 125.91429520013486, (41, 26473): 126.03443151817088, (41, 26476): 127.16533878658286, (41, 26485): 124.69689230528115, (41, 26493): 125.27110867560822, (41, 26524): 123.3091087271771, (41, 26525): 123.49435855456758, (41, 26556): 125.42415981059293, (41, 26560): 124.45415921998736, (41, 26561): 123.67058234158888, (41, 26564): 125.4180814012352, (41, 26569): 123.82120419418615, (41, 26570): 123.9287240590699, (41, 26573): 124.54803814449164, (41, 26581): 124.94806006661037, (41, 26583): 124.48806762109396, (41, 26593): 125.48780723132285, (41, 26837): 126.66781585979733, (41, 26844): 127.08991305223557, (41, 26863): 127.20138695337391, (41, 26893): 128.8295583925012, (41, 26902): 129.44423153638706, (41, 26905): 127.90899253256434, (41, 26912): 128.67910300454162, (41, 26921): 127.91541096319929, (41, 26922): 128.1806079405211, (41, 27212): 110.0221603025182, (41, 27218): 108.49417056347775, (41, 27239): 111.29758104365567, (41, 27257): 111.02206296158174, (41, 27274): 111.68836112647193, (41, 27279): 111.89142380793042, (41, 27282): 111.22600904521923, (41, 27283): 110.85671529096203, (41, 27285): 112.18548436465916, (41, 27286): 112.14071409740633, (41, 27290): 110.7138162206245, (41, 27295): 109.8195329247713, (41, 27300): 111.67581980502388, (41, 27344): 111.37346421506153, (41, 27366): 112.43808300460071, (41, 27383): 112.92345886820036, (41, 27398): 112.9534472272165, (41, 27406): 112.04857296945154, (41, 27407): 111.98850262892945, (41, 27426): 108.92135892352218, (41, 27432): 106.72044991257525, (41, 27460): 107.79024566632476, (41, 27523): 117.7941205742286, (41, 27545): 124.27077491884347, (41, 27602): 143.46272287829774, (41, 27606): 143.44187770436298, (41, 27646): 131.09986031350093, (41, 27667): 134.60459341583228, (41, 27672): 134.55648597660468, (41, 27674): 134.09977274176333, (41, 27688): 133.68474751663402, (41, 27692): 135.43509420722734, (41, 27693): 134.9543014760589, (41, 27705): 135.19198469210622, (41, 27712): 135.65207409670748, (41, 27786): 135.6830127308782, (41, 27790): 130.67144589771107, (41, 27791): 130.07435409268012, (41, 27795): 134.89117784096072, (41, 27801): 131.41990246349252, (41, 27813): 136.59166549885768, (41, 27816): 135.32996181971052, (41, 27823): 131.26203544509846, (41, 27830): 133.8350065886933, (41, 27884): 128.1860221894397, (41, 27885): 130.06606349290468, (41, 27896): 128.76370997389097, (41, 27919): 128.41481418915055, (41, 27922): 129.03965502271453, (41, 27930): 128.11917356878484, (41, 27934): 128.42671399743662, (41, 27935): 128.75003376424584, (41, 27948): 153.0503854364421, (41, 27951): 150.24306676018887, (41, 28061): 166.67062322962397, (41, 28290): 195.09539329218015, (41, 28292): 196.72708149995552, (41, 28293): 195.4878786893252, (41, 28295): 195.78818533028857, (41, 28296): 195.37715778905397, (41, 28297): 194.29318338359843, (41, 28302): 194.5818587543776, (41, 28310): 248.77236727523962, (41, 28313): 250.31040277905097, (41, 28372): 248.63214647459804, (41, 28398): 248.83004876028266, (41, 28399): 248.68792173643052, (41, 28400): 249.153448052451, (41, 28401): 247.70524514483097, (41, 28445): 250.46068597102646, (41, 28475): 245.4968597536489, (41, 28885): 97.24140690107393, (41, 28886): 96.75853897285943, (41, 28915): 95.39115766495561, (41, 28916): 95.7626945317168, (41, 28917): 95.38155916697289, (41, 28921): 97.78519348119566, (41, 28931): 97.36265105236457, (41, 28945): 91.82209775125683, (41, 28982): 93.60631420914798, (41, 29219): 86.18628622450535, (41, 29228): 86.12356737604978, (41, 29246): 83.10436050702931, (41, 29248): 81.53747162517354, (41, 29282): 81.73015209227235, (41, 29290): 84.79853980656655, (41, 29291): 84.32720855897729, (41, 29292): 84.54811495692752, (41, 29293): 84.52150674573473, (41, 29294): 83.89007201564506, (41, 29298): 84.11739133293875, (41, 29299): 83.70306511286701, (41, 29304): 84.59678372259278, (41, 29317): 85.12997846073668, (41, 29323): 85.21993989787501, (41, 29330): 84.8832406931476, (41, 29331): 85.06423760258555, (41, 29344): 83.10523695922319, (41, 29445): 78.18957229825408, (41, 29724): 329.45872650998933, (41, 29738): 329.7883915150225, (41, 29745): 328.9583131624133, (41, 29748): 329.8111564721402, (41, 29750): 330.6276884470535, (41, 29759): 329.2775438214259, (41, 29772): 330.50871239252996, (41, 29781): 330.2588647340033, (41, 29784): 329.76435564522046, (41, 29790): 330.64297539941055, (41, 29811): 330.23287617913513, (41, 29817): 334.1904001368255, (41, 29818): 333.9563522976089, (41, 29929): 328.4254830748879, (41, 30039): 330.8080832553371, (41, 30066): 326.9045787133343, (41, 30116): 317.228723454387, (41, 30238): 302.6238382571181, (41, 30248): 307.8908120762828, (41, 30260): 307.8789937076123, (41, 30545): 101.0637620678429, (41, 30733): 103.43663393085762, (41, 30756): 96.09373535005112, (41, 30921): 98.41297120533443, (41, 31079): 143.6634372246907, (41, 31149): 138.08365362984605, (41, 31154): 139.03957133791607, (41, 31160): 137.96511812839657, (41, 31163): 139.0468659201796, (41, 31189): 137.48771924989518, (41, 31215): 138.4323634147495, (41, 31259): 142.69352694250486, (41, 31262): 142.3179844614899, (41, 31430): 146.59771232411154, (41, 31568): 153.890444496277, (41, 31751): 145.62153256545008, (42, 109): 99.9266689569092, (42, 872): 268.69610430995186, (42, 873): 269.5974702750699, (42, 877): 269.26533713967694, (42, 879): 269.3996238804358, (42, 884): 268.5072378759139, (42, 889): 269.0693334396722, (42, 891): 268.2074512743567, (42, 892): 270.09708683393393, (42, 894): 269.98085884110196, (42, 896): 269.10230866452355, (42, 903): 269.30593318202455, (42, 909): 267.7513982622635, (42, 910): 268.1066502178432, (42, 912): 267.5117146096265, (42, 913): 266.8583015718181, (42, 916): 266.57325681757663, (42, 926): 268.3947489406922, (42, 927): 268.0906951513016, (42, 948): 267.8798081615884, (42, 961): 268.3759217030286, (42, 962): 268.4742726551003, (42, 963): 268.58607843151026, (42, 967): 269.6846121820859, (42, 974): 269.2145426322138, (42, 998): 270.0460401287207, (42, 1014): 289.66907604309057, (42, 1086): 266.2624278644824, (42, 1087): 266.11286455061463, (42, 1089): 265.29751862930584, (42, 1090): 265.68160610190114, (42, 1092): 266.98490798207536, (42, 1097): 265.99783767231224, (42, 1107): 267.6110496087543, (42, 1387): 129.51594237263993, (42, 1554): 115.5228760406814, (42, 1827): 309.80486656254766, (42, 1828): 309.90207971611966, (42, 1829): 310.03876457760003, (42, 1830): 309.8877000686066, (42, 1831): 309.969906354106, (42, 1832): 309.8740171837915, (42, 1833): 309.8863799169009, (42, 1836): 309.7844322973608, (42, 1841): 310.3581847949634, (42, 1843): 310.1168844322553, (42, 1844): 310.22280503716064, (42, 1845): 309.93417527100667, (42, 1847): 309.00854326602996, (42, 1848): 309.3282795879566, (42, 1849): 310.82506853805006, (42, 1850): 310.98340518116163, (42, 1851): 309.56896951216663, (42, 1852): 309.58884928305264, (42, 1854): 309.74475639470967, (42, 1856): 308.95859839180525, (42, 1857): 309.3045941858426, (42, 1858): 310.681872663968, (42, 1861): 310.0156925819494, (42, 1866): 308.9351856562107, (42, 1867): 310.3777199147461, (42, 1868): 310.18671350073845, (42, 1870): 310.19164210503857, (42, 1871): 310.33676188411806, (42, 1875): 309.73089036362495, (42, 1880): 309.1619638678563, (42, 1882): 309.2515981901682, (42, 1883): 310.9997901584142, (42, 1889): 309.3346954158792, (42, 1893): 310.0614211322685, (42, 1894): 309.835761280394, (42, 1899): 309.13710535256695, (42, 1900): 309.3050771683885, (42, 1902): 310.4544303811237, (42, 1905): 310.7445140975931, (42, 1907): 309.5493824960868, (42, 1910): 309.66101722151814, (42, 1917): 311.36936921855016, (42, 1920): 309.5740786976015, (42, 1935): 310.7903619473687, (42, 1937): 311.03834630348064, (42, 1946): 308.6401741682367, (42, 1949): 308.920205452969, (42, 1950): 307.93478117136647, (42, 1951): 308.4088915868869, (42, 1952): 308.75537065269833, (42, 1953): 308.915514732938, (42, 1954): 308.68826907054694, (42, 1958): 308.8382693528412, (42, 1960): 309.3101434737613, (42, 1968): 309.4963504012814, (42, 1969): 310.85268309359043, (42, 1974): 310.49761883594203, (42, 1975): 310.4923978166923, (42, 1979): 309.8223439759868, (42, 1980): 309.7655484734404, (42, 1981): 309.9646955516168, (42, 1985): 310.12773916811415, (42, 1994): 307.54376743933705, (42, 2011): 309.2379239765824, (42, 2019): 311.5784078256903, (42, 2020): 311.2689425125457, (42, 2029): 310.08852797512844, (42, 2030): 311.054516250733, (42, 2032): 309.89273534590205, (42, 2033): 310.5225062960304, (42, 2034): 310.50889244186016, (42, 2036): 309.3174666614657, (42, 2037): 309.62299015594374, (42, 2038): 309.73777134174503, (42, 2042): 313.3143506304066, (42, 2050): 310.36525737235627, (42, 2051): 310.3108252580439, (42, 2053): 310.40701985279725, (42, 2054): 310.72340921480424, (42, 2066): 310.07905128064596, (42, 2067): 310.08253463466264, (42, 2071): 306.94770068524315, (42, 2072): 307.5426700666852, (42, 2073): 305.917702161134, (42, 2074): 305.8363442980869, (42, 2080): 304.8311087325916, (42, 2082): 307.8630919963603, (42, 2083): 308.1708536279069, (42, 2089): 307.52033204550145, (42, 2090): 307.8076319313736, (42, 2092): 307.4174588680677, (42, 2098): 305.2163880367398, (42, 2099): 305.5617010977106, (42, 2101): 305.15316534229885, (42, 2102): 306.77460033162185, (42, 2103): 306.26449804847056, (42, 2104): 305.9851702476622, (42, 2106): 308.3777255712595, (42, 2112): 305.3681076974706, (42, 2113): 307.0050028905171, (42, 2114): 307.3946026924515, (42, 2117): 308.62023078308846, (42, 2123): 306.20855977674086, (42, 2124): 306.5427282018354, (42, 2134): 305.59995131755284, (42, 2138): 306.5795285026154, (42, 2141): 305.71292545540024, (42, 2148): 306.2333271672564, (42, 2150): 304.90129647475385, (42, 2151): 305.2556252749249, (42, 2152): 304.7189352875625, (42, 2153): 306.3435636640676, (42, 2154): 304.9570586801834, (42, 2155): 304.8022548529764, (42, 2156): 304.54132245112703, (42, 2157): 304.9079499376219, (42, 2160): 307.06342251163835, (42, 2161): 304.6647380102359, (42, 2162): 306.4116387467148, (42, 2163): 305.9412914850505, (42, 2164): 305.91132540245843, (42, 2168): 305.053662324323, (42, 2172): 305.37916869444797, (42, 2174): 305.21958678817947, (42, 2178): 305.6569796183488, (42, 2179): 305.44176369462167, (42, 2183): 306.56092742919094, (42, 2185): 306.5842053910727, (42, 2186): 306.3162722612953, (42, 2190): 307.12527339616855, (42, 2192): 306.64364814005444, (42, 2193): 306.6533533274996, (42, 2194): 306.16133027272014, (42, 2195): 306.0950132247862, (42, 2197): 306.75134344239495, (42, 2205): 306.06927920663935, (42, 2207): 305.1800968030695, (42, 2208): 305.67830095622264, (42, 2212): 306.7859755287434, (42, 2214): 296.9317271512225, (42, 2225): 298.1163164410684, (42, 2231): 295.7091702160992, (42, 2278): 303.01102128854734, (42, 2284): 304.0215084125961, (42, 2285): 303.8803486924502, (42, 2291): 301.8734692889866, (42, 2292): 302.09376219590195, (42, 2307): 303.3649838214733, (42, 2313): 301.6348062721293, (42, 2317): 301.34701600766823, (42, 2319): 302.4412860901531, (42, 2321): 302.9049007287851, (42, 2323): 302.84405129953024, (42, 2326): 304.61034435851394, (42, 2327): 304.17298159939867, (42, 2329): 303.87448805435014, (42, 2330): 303.5344978707881, (42, 2332): 304.25502317277386, (42, 2344): 303.13935714410866, (42, 2346): 303.1192213915923, (42, 2361): 302.9417146358917, (42, 2368): 308.05004874833446, (42, 2374): 308.53180630330604, (42, 2375): 308.69268755752563, (42, 2377): 307.01137557886454, (42, 2378): 308.9960873973072, (42, 2379): 309.0385796806767, (42, 2380): 309.2045058973354, (42, 2383): 307.45947819596853, (42, 2385): 307.71881756964643, (42, 2395): 307.74703180408267, (42, 2397): 308.838733906278, (42, 2398): 306.47574510867446, (42, 2399): 307.08033248756055, (42, 2400): 306.9446793552792, (42, 2402): 307.90562225009654, (42, 2403): 308.28129495379227, (42, 2404): 308.3781413381682, (42, 2405): 307.47271509462934, (42, 2407): 308.21035939101415, (42, 2408): 308.65121180605945, (42, 2409): 307.74738064702126, (42, 2411): 308.277828539087, (42, 2412): 308.17960118611353, (42, 2413): 308.4876502075443, (42, 2414): 307.98651133018933, (42, 2422): 308.1630521372737, (42, 2424): 308.285814655031, (42, 2426): 308.3673532638304, (42, 2433): 307.666812777555, (42, 2436): 307.4798821848031, (42, 2437): 305.28660323618783, (42, 2440): 305.77015560308683, (42, 2445): 315.44717173797693, (42, 2447): 314.2591880439242, (42, 2454): 315.38095385093595, (42, 2455): 315.44643017970225, (42, 2460): 311.958788245368, (42, 2461): 312.38860057286337, (42, 2471): 319.3167652929312, (42, 2492): 311.68523426054935, (42, 2511): 308.262801954066, (42, 2523): 310.0127836591878, (42, 2525): 309.46830023760435, (42, 2535): 310.54755556542176, (42, 2537): 309.7730992201951, (42, 2538): 310.3154114209169, (42, 2539): 310.0500553070211, (42, 2540): 310.89788910252133, (42, 2542): 311.4446619365192, (42, 2559): 322.4840597645422, (42, 2575): 321.44637756588116, (42, 2599): 304.950479102183, (42, 2600): 308.6456905666331, (42, 2607): 306.534412533503, (42, 2627): 310.2183127625347, (42, 2647): 312.2125649035391, (42, 2674): 311.23169533348954, (42, 2681): 310.9176604658504, (42, 2683): 311.92512114897204, (42, 2686): 310.799485602886, (42, 2689): 324.02191446822155, (42, 2690): 324.07845845118396, (42, 2713): 326.3948616523662, (42, 2714): 326.58280843849406, (42, 2715): 326.91041806893446, (42, 2739): 326.63013576315143, (42, 2740): 324.65852504580363, (42, 2741): 324.82803757502154, (42, 2749): 326.1408227419904, (42, 2750): 326.2557202420987, (42, 2752): 326.4949678330634, (42, 2755): 326.74614539845754, (42, 2758): 326.66004575793033, (42, 2759): 326.6667889678998, (42, 2769): 326.30045903548955, (42, 2771): 325.1630970657507, (42, 2779): 325.17711447454474, (42, 2784): 321.4513650999355, (42, 2800): 322.02001693368624, (42, 2802): 323.97855981304156, (42, 2803): 323.8646919705334, (42, 2804): 323.65007599784457, (42, 2805): 324.2217696639209, (42, 2807): 324.2123204323005, (42, 2809): 324.06581379284717, (42, 2812): 321.99188175122583, (42, 2814): 323.88083588998603, (42, 2817): 323.84898414244475, (42, 2819): 324.28171770425246, (42, 2823): 322.099860657836, (42, 2832): 324.6130623293709, (42, 2836): 323.1396661561802, (42, 2839): 324.21869427618594, (42, 2841): 323.97504827675283, (42, 2843): 323.8841200679055, (42, 2846): 323.38531792178196, (42, 2849): 324.8241411230554, (42, 2852): 324.49669388724084, (42, 2853): 324.97415918282906, (42, 2876): 325.07026536337395, (42, 2877): 326.2442066522898, (42, 2885): 326.4896455306285, (42, 2918): 324.5162927977837, (42, 2921): 325.01256380715694, (42, 2925): 322.7130650258118, (42, 2926): 321.96048296469246, (42, 2930): 323.6035279444949, (42, 2931): 322.906458908408, (42, 2938): 324.5049591670588, (42, 2940): 326.0638796955284, (42, 2947): 324.3478055757021, (42, 2949): 323.6286420856587, (42, 2950): 323.8399677063742, (42, 2952): 323.58846998506294, (42, 2958): 323.54667005659377, (42, 2959): 323.8084856783908, (42, 2960): 324.3609521218095, (42, 2961): 324.08466178632386, (42, 2963): 323.3240159066983, (42, 2968): 323.47339578333157, (42, 2976): 323.2677349808161, (42, 2981): 318.36448248926143, (42, 2982): 318.2052098908128, (42, 2984): 317.95168326509406, (42, 3003): 317.49096186347117, (42, 3046): 314.46864213616436, (42, 3050): 316.9204090661773, (42, 3051): 317.12470302940426, (42, 3053): 316.5676872026889, (42, 3069): 319.5997545928618, (42, 3071): 316.48068955663115, (42, 3080): 326.45639354484905, (42, 3199): 316.54414416314324, (42, 3200): 315.949341336173, (42, 3205): 319.5348317568584, (42, 3209): 316.24966775640695, (42, 3215): 315.9973721016749, (42, 3217): 315.28039968822907, (42, 3249): 316.0752994599369, (42, 3263): 321.49406784593543, (42, 3289): 317.8187744316646, (42, 3301): 317.96035972123605, (42, 3302): 317.7133326347179, (42, 3307): 317.394690494388, (42, 3310): 318.2689429554542, (42, 3391): 318.25547700751434, (42, 3509): 203.17478483049092, (42, 3510): 202.66523616245317, (42, 3511): 203.01896530464313, (42, 3512): 202.71626667749823, (42, 3514): 202.83462069754998, (42, 3519): 204.29880865301024, (42, 3536): 204.09893591424773, (42, 3545): 204.91288107779647, (42, 3548): 204.14986051366486, (42, 3572): 204.37097713604643, (42, 3581): 203.70546524035774, (42, 3583): 203.4178718018325, (42, 3601): 205.2330551507527, (42, 3656): 204.34894872794493, (42, 3669): 203.22676387766612, (42, 3670): 203.67837390912746, (42, 3695): 201.1204152435145, (42, 3696): 201.48369941107313, (42, 3782): 204.5630916487938, (42, 3792): 203.96998329180494, (42, 3989): 21.764286568626474, (42, 4008): 24.357629934336035, (42, 4031): 25.437820095000703, (42, 4045): 23.319755668023856, (42, 4144): 22.332447986281274, (42, 4145): 18.47552783688362, (42, 4164): 21.02426924874719, (42, 4168): 19.640182283966897, (42, 4173): 19.19911592913139, (42, 4181): 17.57445375586799, (42, 4228): 17.44726922657683, (42, 4248): 14.944909605200914, (42, 4254): 12.5, (42, 4260): 12.5, (42, 4262): 12.5, (42, 4273): 12.5, (42, 4319): 15.609592664226897, (42, 4326): 15.776844058733628, (42, 4328): 15.495544218019745, (42, 4334): 15.39242276022238, (42, 4335): 15.724517179050098, (42, 4372): 99.96460069327365, (42, 4413): 105.07951642899137, (42, 4434): 99.23607652683766, (42, 4447): 97.67532303623561, (42, 4452): 99.5702156189428, (42, 4463): 107.93642296028185, (42, 4465): 107.28327411497357, (42, 4619): 111.41158956860816, (42, 4645): 110.65352551095592, (42, 4657): 111.37424316598714, (42, 4666): 111.97603641225707, (42, 4676): 112.07832492651306, (42, 4678): 111.7493969444092, (42, 4689): 112.56207504263067, (42, 4704): 113.38326101067592, (42, 4726): 132.2488769270226, (42, 4727): 131.9587679549584, (42, 4730): 131.348797076547, (42, 4731): 131.84186552406655, (42, 4734): 130.33793682160555, (42, 4735): 130.33763493621174, (42, 4736): 130.7143635902005, (42, 4737): 130.5517066248675, (42, 4738): 130.8090600536104, (42, 4756): 131.24444847676006, (42, 4760): 128.45277949565514, (42, 4761): 128.0754109273885, (42, 4762): 128.38749296383094, (42, 4765): 128.75605398427373, (42, 4773): 132.5555295902085, (42, 4774): 132.7341218693539, (42, 4790): 132.29683198377475, (42, 4795): 131.9335229557221, (42, 4799): 133.0912062860232, (42, 4801): 134.2967701542176, (42, 4804): 131.48374439815905, (42, 4805): 131.19151754211165, (42, 4806): 133.26889129693353, (42, 4815): 133.37610787041555, (42, 4816): 133.90277871908282, (42, 4817): 134.54864826542553, (42, 4826): 133.96205352448365, (42, 4830): 133.76574296849012, (42, 4839): 129.31740639370395, (42, 4840): 129.7928886855177, (42, 4841): 129.36245427126906, (42, 4846): 129.07707575951156, (42, 4848): 129.45074578855602, (42, 4850): 129.78669735884878, (42, 4871): 124.45528950978992, (42, 4883): 127.48863722984653, (42, 4900): 125.30443949432184, (42, 4901): 125.30252928795423, (42, 4917): 120.08558804787506, (42, 4931): 118.86446911692964, (42, 4944): 119.89717058386385, (42, 4956): 119.41429143418857, (42, 4958): 120.02901117836862, (42, 4959): 120.2454792342791, (42, 4961): 119.3943091321322, (42, 4966): 119.49674397553464, (42, 5207): 118.25919912492273, (42, 5272): 83.42611878573302, (42, 5283): 83.67182403143529, (42, 5287): 85.60245474955543, (42, 5289): 85.78055763876357, (42, 5293): 81.99814131848751, (42, 5295): 82.48320719334502, (42, 5296): 83.40542420859431, (42, 5298): 83.91565786151928, (42, 5303): 84.87360485034964, (42, 5305): 85.10983310081859, (42, 5306): 86.27850943706856, (42, 5307): 85.10058165856698, (42, 5308): 85.4893384992104, (42, 5313): 84.32239165865792, (42, 5314): 84.08477773335298, (42, 5317): 86.09109920803137, (42, 5319): 84.90499090142093, (42, 5324): 84.08841800851881, (42, 5326): 83.51240250538555, (42, 5348): 87.0287767770091, (42, 5351): 88.44593978846619, (42, 5399): 87.25581735863254, (42, 5413): 90.7311725724231, (42, 5422): 86.44423025608431, (42, 5445): 86.40533470595906, (42, 5448): 86.24740518864515, (42, 5456): 87.18899972915477, (42, 5467): 87.59755445243711, (42, 5624): 83.33622916970178, (42, 5671): 76.55495971605032, (42, 5672): 76.00198212406136, (42, 5797): 83.60885880033015, (42, 5871): 99.61076180160254, (42, 5976): 96.94998501217444, (42, 6118): 263.80651824139085, (42, 6248): 274.40261756601944, (42, 6345): 88.38755759415184, (42, 6352): 90.86257510625198, (42, 6354): 87.76254474961829, (42, 6359): 87.31275419360716, (42, 6376): 90.5841727212552, (42, 6378): 88.05933005858716, (42, 6381): 87.54265417412847, (42, 6383): 88.89593020034101, (42, 6396): 88.0092187481907, (42, 6399): 88.40601568002162, (42, 6408): 90.73029813421576, (42, 6409): 89.47303331635224, (42, 6419): 93.3074001618302, (42, 6422): 90.32661398926167, (42, 6423): 90.52015240445407, (42, 6424): 87.90415556048065, (42, 6439): 88.34910638706678, (42, 6464): 89.00359276664838, (42, 6465): 89.27505095365835, (42, 6469): 89.0321782922967, (42, 6470): 89.19904358475884, (42, 6472): 86.49097334809412, (42, 6480): 86.85294304458671, (42, 6486): 85.30412200407558, (42, 6497): 85.80910798672201, (42, 6503): 88.71928408684055, (42, 6508): 88.60601701143065, (42, 6509): 88.10743065399205, (42, 6521): 86.49476046772654, (42, 6544): 86.6015272478929, (42, 6552): 89.76012914719874, (42, 6553): 90.13152671944778, (42, 6554): 90.5103634720604, (42, 6578): 89.15015302285335, (42, 6582): 89.35876735404632, (42, 6601): 88.96365974721523, (42, 6609): 86.0448181603575, (42, 6610): 85.91792942787275, (42, 6611): 85.8976934684155, (42, 6614): 86.12917346493509, (42, 6615): 86.03863021936063, (42, 6616): 85.57524566789526, (42, 6617): 85.77093767088942, (42, 6618): 85.1527509559077, (42, 6619): 86.3904314273683, (42, 6620): 85.53727293804289, (42, 6621): 85.85129270027002, (42, 6622): 85.7965864705423, (42, 6623): 86.12317386783108, (42, 6624): 86.37263783233466, (42, 6625): 86.4509985356676, (42, 6626): 86.42508858817698, (42, 6627): 86.2427454465406, (42, 6628): 85.57587261724049, (42, 6629): 86.24514784396884, (42, 6630): 86.78565980891295, (42, 6632): 86.294874066263, (42, 6634): 87.1080336858074, (42, 6635): 85.9819688606827, (42, 6636): 85.54658810016744, (42, 6637): 86.68149601719767, (42, 6638): 86.71065467898306, (42, 6639): 86.18620672780081, (42, 6640): 86.67537368015552, (42, 6641): 85.83822769071128, (42, 6642): 86.6795746216826, (42, 6643): 86.48984502981077, (42, 6645): 86.32864521275816, (42, 6646): 85.29017669907412, (42, 6647): 86.59587592367964, (42, 6653): 86.06465677240801, (42, 6655): 86.19541531363986, (42, 6658): 87.1174450563581, (42, 6662): 86.67398451550935, (42, 6819): 104.64876974751398, (42, 6996): 98.58282556884885, (42, 7059): 94.36515714445594, (42, 7187): 103.65757333807879, (42, 7304): 111.01644877056441, (42, 7528): 99.53630425605796, (42, 7720): 74.1457591352559, (42, 7793): 75.0040934965371, (42, 7807): 74.5416239417432, (42, 7808): 75.22122658241285, (42, 7831): 83.5510572534447, (42, 7850): 79.59274194588187, (42, 7852): 80.56599694151261, (42, 8012): 75.01151599074723, (42, 8125): 75.29872705401424, (42, 8208): 66.61263858835717, (42, 8392): 80.59937100796348, (42, 8651): 125.10865011858375, (42, 9088): 106.76221735733027, (42, 9443): 136.2472843898362, (42, 9444): 135.70941368620376, (42, 9828): 156.15170313911995, (42, 9868): 155.17281887059323, (42, 10180): 75.37544640785671, (42, 10256): 66.45528720085645, (42, 10276): 69.58923065355397, (42, 10378): 65.91527501521297, (42, 10676): 83.19818618661722, (42, 10714): 90.4878063159602, (42, 10730): 85.85260574336249, (42, 10862): 141.54459412015308, (42, 10881): 141.1525646808006, (42, 10883): 141.45237069844015, (42, 10885): 141.5665601875471, (42, 10891): 141.9245919875634, (42, 10909): 141.3468926764032, (42, 10911): 140.66389479483814, (42, 10913): 140.95719678783428, (42, 10915): 140.63771965522173, (42, 10919): 140.31100028441261, (42, 11037): 150.76551211117066, (42, 11039): 149.29878525295211, (42, 11516): 60.77167202743798, (42, 11856): 15.221562017059833, (42, 11857): 16.42450150510234, (42, 11861): 15.830991859901413, (42, 11881): 15.005668992661171, (42, 11902): 16.406357333789977, (42, 11911): 15.962642316835948, (42, 11914): 16.055250875446742, (42, 11922): 15.24125755533609, (42, 11924): 14.707902221430738, (42, 11926): 15.06861266953877, (42, 11950): 13.418419991602061, (42, 11963): 12.5, (42, 11983): 12.5, (42, 11985): 12.5, (42, 12009): 12.5, (42, 12010): 12.5, (42, 12018): 12.5, (42, 12020): 12.5, (42, 12021): 12.5, (42, 12024): 12.5, (42, 12025): 12.5, (42, 12027): 12.5, (42, 12031): 12.5, (42, 12032): 12.5, (42, 12035): 12.5, (42, 12041): 12.5, (42, 12045): 25.245742127702204, (42, 12145): 17.57403864198281, (42, 12275): 25.581644980943416, (42, 12294): 25.92753342576038, (42, 12358): 32.66237991256403, (42, 12463): 36.66610947758319, (42, 12465): 36.68451782919359, (42, 12482): 36.466888385128925, (42, 12503): 36.631238863519336, (42, 12506): 36.907588633308464, (42, 12549): 34.79315162978163, (42, 12559): 34.876758057624166, (42, 12569): 35.64343672705668, (42, 12572): 35.821903604530284, (42, 12574): 35.282505775050296, (42, 12576): 34.865515700179294, (42, 12591): 33.98481030016568, (42, 12608): 35.29642849678331, (42, 12696): 31.773042820313098, (42, 12710): 32.54618404427782, (42, 12728): 32.72528458650589, (42, 12766): 55.79625390328459, (42, 12771): 56.878883172618686, (42, 12790): 57.35712719262165, (42, 12795): 58.67505171258254, (42, 12797): 61.66652003787186, (42, 12798): 61.05683359020112, (42, 12811): 57.95988861796462, (42, 12830): 59.29162951086388, (42, 12848): 58.15289010283511, (42, 12850): 57.54562707823495, (42, 12852): 59.256413851018785, (42, 12854): 59.735712135724334, (42, 12859): 57.52045213891209, (42, 12861): 60.39483000195967, (42, 12865): 57.65186822950194, (42, 12866): 57.71028314581193, (42, 12867): 56.930377492180966, (42, 12874): 57.3328812676979, (42, 12875): 56.89463698394272, (42, 12881): 58.57814035972316, (42, 12883): 57.97055169321114, (42, 12885): 56.627341457978204, (42, 12888): 58.12030206911177, (42, 12889): 58.134476771156315, (42, 12892): 57.30387585978176, (42, 12893): 58.22563863262603, (42, 12896): 57.81339308884413, (42, 12906): 57.88877722185738, (42, 13018): 65.86259755057628, (42, 13071): 66.75607420330786, (42, 13131): 67.12749435199203, (42, 13146): 63.3287038258151, (42, 13159): 71.83624913105567, (42, 13193): 67.54195321073355, (42, 13198): 72.25999780872603, (42, 13292): 65.28696016060434, (42, 13296): 62.37182446272144, (42, 13406): 77.53775603956115, (42, 13407): 77.8684771051063, (42, 13417): 79.48659325085234, (42, 13418): 79.0789486313569, (42, 13438): 75.60637335272766, (42, 13442): 74.70641216350731, (42, 13443): 75.24220522650772, (42, 13764): 126.57755341738645, (42, 13766): 125.92058463981164, (42, 13771): 127.02117419219832, (42, 13783): 126.3806192234409, (42, 13784): 125.00753570889768, (42, 13792): 128.98903107289226, (42, 13824): 126.9208682092844, (42, 14017): 120.60312376797414, (42, 14870): 128.63074567247887, (42, 14997): 106.93688315223226, (42, 15000): 106.94638645510604, (42, 15003): 106.58659112725985, (42, 15006): 105.28138178152486, (42, 15007): 104.84377773153393, (42, 15056): 105.11866477402388, (42, 15063): 105.55983085160467, (42, 15069): 105.79952965339061, (42, 15076): 104.82222980064442, (42, 15086): 106.13239989963702, (42, 15087): 106.7042169328226, (42, 15111): 107.97459871202602, (42, 15116): 107.25089533399711, (42, 15722): 119.02653245283024, (42, 15998): 129.1366111555587, (42, 16073): 223.59388982607433, (42, 16939): 281.22693189910706, (42, 16940): 280.5676156856644, (42, 16951): 281.29761912643926, (42, 16963): 281.36614936240983, (42, 16965): 282.1775379782078, (42, 16969): 281.96971145159694, (42, 16970): 281.663893966762, (42, 16971): 280.9335778518276, (42, 16973): 280.8771689710368, (42, 16974): 282.4966374950702, (42, 16976): 281.72509974209646, (42, 16978): 281.1940924666908, (42, 16980): 282.0010722124389, (42, 16982): 282.48317340180495, (42, 17045): 303.9153110476778, (42, 17048): 304.8526842322582, (42, 17304): 12.5, (42, 17305): 12.5, (42, 17330): 12.5, (42, 17334): 12.5, (42, 17343): 12.5, (42, 17345): 12.5, (42, 17347): 12.5, (42, 17351): 12.5, (42, 17372): 12.5, (42, 17373): 12.5, (42, 17377): 12.5, (42, 17382): 12.5, (42, 17383): 12.5, (42, 17389): 12.5, (42, 17400): 12.5, (42, 17401): 12.5, (42, 17402): 12.5, (42, 17403): 12.5, (42, 17440): 12.5, (42, 17455): 12.5, (42, 17491): 12.5, (42, 17507): 12.5, (42, 17509): 12.5, (42, 17590): 12.5, (42, 17615): 12.5, (42, 17642): 12.5, (42, 17643): 12.5, (42, 17668): 12.5, (42, 17721): 12.5, (42, 17754): 12.5, (42, 17769): 12.5, (42, 17776): 12.5, (42, 17804): 12.5, (42, 17809): 12.5, (42, 17824): 12.5, (42, 17837): 12.5, (42, 17838): 12.5, (42, 17862): 12.5, (42, 17866): 12.5, (42, 17872): 12.5, (42, 17873): 12.5, (42, 17881): 12.5, (42, 17947): 226.9874908579201, (42, 17951): 225.74613905620316, (42, 17953): 225.49652485062177, (42, 17954): 225.5752101586257, (42, 17959): 226.75378764853266, (42, 17963): 226.3375899087449, (42, 18000): 219.98615568729423, (42, 18001): 220.21906542421561, (42, 18111): 237.35386624249483, (42, 18148): 205.44154991575098, (42, 18166): 217.73201834310223, (42, 18189): 229.3181475328303, (42, 18239): 12.5, (42, 18240): 12.5, (42, 18245): 12.5, (42, 18247): 12.5, (42, 18251): 12.5, (42, 18256): 12.5, (42, 18258): 12.5, (42, 18259): 12.5, (42, 18260): 12.5, (42, 18262): 12.5, (42, 18263): 12.5, (42, 18264): 12.5, (42, 18266): 12.5, (42, 18267): 12.5, (42, 18268): 12.5, (42, 18269): 12.5, (42, 18275): 12.5, (42, 18285): 12.5, (42, 18308): 12.5, (42, 18313): 12.5, (42, 18314): 12.5, (42, 18315): 12.5, (42, 18316): 12.5, (42, 18317): 12.5, (42, 18320): 12.5, (42, 18321): 12.5, (42, 18322): 12.5, (42, 18324): 12.5, (42, 18325): 12.5, (42, 18326): 12.5, (42, 18327): 12.5, (42, 18329): 12.5, (42, 18330): 12.5, (42, 18331): 12.5, (42, 18332): 12.5, (42, 18333): 12.5, (42, 18336): 12.5, (42, 18337): 12.5, (42, 18403): 12.587101100173825, (42, 18432): 14.577932687430641, (42, 18451): 13.018107312758467, (42, 18466): 12.5, (42, 18481): 12.5, (42, 18483): 12.5, (42, 18484): 12.5, (42, 18485): 12.5, (42, 18486): 12.5, (42, 18487): 12.5, (42, 18489): 12.5, (42, 18490): 12.5, (42, 18491): 12.5, (42, 18492): 12.5, (42, 18493): 12.5, (42, 18494): 12.5, (42, 18495): 12.5, (42, 18496): 12.5, (42, 18497): 12.5, (42, 18498): 12.5, (42, 18499): 12.5, (42, 18501): 12.5, (42, 18502): 12.5, (42, 18503): 12.5, (42, 18504): 12.5, (42, 18506): 12.5, (42, 18507): 12.5, (42, 18508): 12.5, (42, 18509): 12.5, (42, 18510): 12.5, (42, 18511): 12.5, (42, 18512): 12.5, (42, 18515): 12.5, (42, 18516): 12.5, (42, 18517): 12.5, (42, 18518): 12.5, (42, 18519): 12.5, (42, 18520): 12.5, (42, 18522): 12.5, (42, 18523): 12.5, (42, 18532): 12.5, (42, 18535): 12.5, (42, 18537): 12.5, (42, 18539): 12.5, (42, 18540): 12.5, (42, 18541): 12.5, (42, 18542): 12.5, (42, 18543): 12.5, (42, 18546): 12.5, (42, 18555): 12.5, (42, 18556): 12.5, (42, 18565): 12.5, (42, 18567): 12.5, (42, 18568): 12.5, (42, 18577): 12.63193254936391, (42, 18583): 12.67340721401749, (42, 18605): 13.174348519599107, (42, 18608): 12.5, (42, 18616): 14.17249291937823, (42, 18618): 14.961992375599705, (42, 18625): 15.175145258009433, (42, 18645): 14.675452419060198, (42, 18646): 14.660749877965602, (42, 18653): 13.379600594681733, (42, 18654): 14.059923182708063, (42, 18655): 13.490926583559618, (42, 18666): 17.337771689791737, (42, 18837): 27.144324395786406, (42, 18974): 15.94653475173658, (42, 18999): 17.856416931097964, (42, 19000): 18.00346577061085, (42, 19174): 28.049000874707176, (42, 19342): 29.199335536511633, (42, 19455): 20.4088119573238, (42, 19555): 34.850953879403896, (42, 19564): 37.0857290205279, (42, 19573): 36.93827316239148, (42, 19586): 36.69166633757615, (42, 19605): 36.02329756590618, (42, 19611): 35.98540261669787, (42, 19614): 35.198701558773315, (42, 19641): 31.76473268117732, (42, 19702): 32.91283815275748, (42, 19713): 32.85344745231846, (42, 19731): 33.394152480383866, (42, 19819): 23.916767072102033, (42, 19893): 49.26489302292019, (42, 19899): 50.660173659581304, (42, 19929): 48.77117128166336, (42, 19951): 49.180413054281445, (42, 19962): 50.27686452777399, (42, 19970): 47.0877544344843, (42, 19971): 47.81918884463897, (42, 19972): 48.36609134698944, (42, 19975): 47.86732999883614, (42, 19978): 45.894033057209676, (42, 19987): 45.38523366597973, (42, 19989): 45.13248201183374, (42, 20039): 45.18828996159055, (42, 20043): 44.6018811785461, (42, 20047): 43.84009895388209, (42, 20052): 44.15245903086594, (42, 20054): 44.50782382616261, (42, 20085): 41.9590826358818, (42, 20104): 42.039685542592686, (42, 20132): 42.50488224570393, (42, 20203): 55.914219697291145, (42, 20280): 58.12793949944929, (42, 20285): 59.05016875787693, (42, 20290): 57.68136466173194, (42, 20297): 57.569161577833604, (42, 20309): 51.589016633740776, (42, 20453): 49.22065221907238, (42, 20485): 57.42539369532228, (42, 20520): 57.36789000530111, (42, 20526): 59.57842710807277, (42, 20698): 153.03581014962862, (42, 20868): 176.61323151083928, (42, 21042): 54.472696183151285, (42, 21057): 49.63921025977786, (42, 21066): 52.08153992629541, (42, 21075): 52.88912857927661, (42, 21093): 54.226441650249825, (42, 21098): 51.01955170947986, (42, 21127): 54.13184712944882, (42, 21130): 53.27996273272701, (42, 21144): 53.306859078265155, (42, 21146): 54.447842272417255, (42, 21147): 53.36204585199229, (42, 21148): 52.55334485564792, (42, 21153): 54.46606218885982, (42, 21293): 46.601178956835604, (42, 21426): 48.65574794042988, (42, 21442): 44.61438291863144, (42, 21451): 44.231167064255025, (42, 21466): 46.41087149018345, (42, 21469): 45.64220829786708, (42, 21471): 46.8076965709631, (42, 21473): 46.13314806689577, (42, 21475): 46.69340635412458, (42, 21482): 45.29148233900064, (42, 21484): 45.37961694804692, (42, 21488): 45.86699593649275, (42, 21494): 46.524987178996845, (42, 21498): 45.99485310235237, (42, 21500): 46.70762656029415, (42, 21514): 44.71968009501378, (42, 21537): 46.54962887180956, (42, 21662): 43.796895875832696, (42, 21691): 46.73406151979978, (42, 21757): 52.77716667009992, (42, 21777): 64.37524027563765, (42, 21778): 65.11352025508636, (42, 21779): 64.82167221739415, (42, 21790): 63.420892745992674, (42, 21802): 63.68996637279734, (42, 21824): 63.054285027559764, (42, 21874): 64.78994523170329, (42, 21879): 65.48274590579528, (42, 21983): 61.25422566595516, (42, 22002): 53.991337356613144, (42, 22132): 58.324457360422294, (42, 22261): 164.16738437472497, (42, 22298): 162.78982088375713, (42, 22339): 172.04505862226688, (42, 22508): 149.33918983352012, (42, 22841): 312.939077633659, (42, 22842): 312.9836888345364, (42, 22874): 311.3112524272631, (42, 22941): 311.3581066411837, (42, 22956): 312.50024819457883, (42, 22960): 312.7284871299879, (42, 22968): 314.3672044903273, (42, 22970): 314.59403183951775, (42, 22974): 315.4714357807522, (42, 22980): 316.80517574795164, (42, 23025): 317.1262456638472, (42, 23028): 316.91961940483253, (42, 23081): 319.6911328826251, (42, 23104): 317.9628888905234, (42, 23147): 305.0154911577598, (42, 23298): 31.42172883821194, (42, 23376): 33.518325822858465, (42, 23381): 34.696377188627004, (42, 23529): 29.90674012033431, (42, 23556): 31.14806539712493, (42, 23718): 33.07907660160521, (42, 24001): 19.546673382526905, (42, 24094): 14.656052879335766, (42, 24129): 12.564801480436826, (42, 24174): 17.00565567929242, (42, 24235): 12.5, (42, 24259): 12.5, (42, 24260): 12.5, (42, 24261): 12.5, (42, 24305): 12.5, (42, 24306): 12.5, (42, 24307): 12.5, (42, 24308): 17.113068886476864, (42, 24498): 12.5, (42, 24499): 12.5, (42, 24500): 12.5, (42, 24668): 12.5, (42, 24711): 12.5, (42, 24756): 12.5, (42, 24788): 12.5, (42, 24809): 12.5, (42, 24813): 12.5, (42, 24821): 12.5, (42, 24825): 12.5, (42, 24832): 12.5, (42, 24833): 12.5, (42, 24835): 12.5, (42, 24837): 12.5, (42, 24840): 12.5, (42, 24841): 12.5, (42, 24844): 12.5, (42, 24845): 12.5, (42, 24846): 12.5, (42, 24849): 12.5, (42, 24850): 12.5, (42, 24863): 12.5, (42, 24866): 12.5, (42, 24885): 12.5, (42, 24886): 12.5, (42, 24889): 12.5, (42, 24903): 12.5, (42, 24909): 12.5, (42, 24999): 30.948450634690303, (42, 25019): 30.9893148289862, (42, 25028): 30.361976078780042, (42, 25137): 67.08486781489489, (42, 25145): 66.65504449408455, (42, 25208): 71.25178453911649, (42, 25233): 71.9169558496917, (42, 25371): 61.56747782388971, (42, 25377): 61.215627537033235, (42, 25828): 88.01997777350127, (42, 25851): 91.04337086220573, (42, 25874): 86.71395751485494, (42, 25898): 86.80542243366139, (42, 25946): 88.39815964376261, (42, 26047): 83.33521233743996, (42, 26066): 60.041352323059435, (42, 26197): 73.0182565850108, (42, 26212): 111.93827344179927, (42, 26253): 114.33522625103878, (42, 26254): 113.27456621839575, (42, 26257): 112.9099913584859, (42, 26258): 113.99062874955928, (42, 26260): 113.39929162746229, (42, 26266): 113.24685322319553, (42, 26267): 112.7075543895859, (42, 26271): 112.81425472609067, (42, 26304): 103.9129013226447, (42, 26305): 103.64905410186891, (42, 26363): 92.44262787264371, (42, 26441): 167.9187858774891, (42, 26442): 167.69824331225954, (42, 26450): 166.49251679418248, (42, 26459): 166.291164913666, (42, 26462): 166.41254730424134, (42, 26467): 169.93215177490666, (42, 26471): 168.99916383607265, (42, 26472): 168.91037744192437, (42, 26473): 168.88508610284075, (42, 26476): 168.47991509741485, (42, 26485): 166.94179392880434, (42, 26493): 167.03366760035846, (42, 26524): 166.89318026851626, (42, 26525): 166.78413336061243, (42, 26556): 168.51809105558786, (42, 26560): 168.31315222682449, (42, 26561): 167.5317541981673, (42, 26564): 168.21764358638168, (42, 26569): 167.37582038449037, (42, 26570): 167.1070333098028, (42, 26573): 167.34942991687367, (42, 26581): 167.3663296149866, (42, 26583): 167.07581299557344, (42, 26593): 167.43156803864167, (42, 26837): 170.21588039668393, (42, 26844): 170.9989927808513, (42, 26863): 169.40392966300533, (42, 26893): 171.70187111748334, (42, 26902): 172.768993611907, (42, 26905): 171.59100676981686, (42, 26912): 172.45513575463593, (42, 26921): 170.49785327758912, (42, 26922): 168.51915596484824, (42, 27212): 173.40618164711944, (42, 27218): 172.34172635482716, (42, 27239): 174.96822256603662, (42, 27257): 174.19972264416072, (42, 27274): 175.30008628329904, (42, 27279): 175.16478782169332, (42, 27282): 174.25509827791421, (42, 27283): 174.54363355082995, (42, 27285): 175.7337536204048, (42, 27286): 174.96343212177808, (42, 27290): 173.4835131749583, (42, 27295): 172.86856984815486, (42, 27300): 175.44268556270328, (42, 27344): 173.1718977336504, (42, 27366): 174.23700406171554, (42, 27383): 175.8890015401477, (42, 27398): 176.91062761520263, (42, 27406): 175.97942612705882, (42, 27407): 176.21917587679062, (42, 27426): 174.7802245018723, (42, 27432): 170.91864535205028, (42, 27460): 173.30357912414675, (42, 27523): 175.11190739213404, (42, 27545): 190.60114758122793, (42, 27602): 211.56338606635592, (42, 27606): 211.90081745058106, (42, 27646): 190.8973867726047, (42, 27667): 195.06261795159662, (42, 27672): 195.2540776222718, (42, 27674): 194.5607864864178, (42, 27688): 195.0490981911105, (42, 27692): 196.00536052241586, (42, 27693): 195.38746071981086, (42, 27705): 195.38535078684868, (42, 27712): 195.71498032782077, (42, 27786): 211.3064193760043, (42, 27790): 208.50433136512285, (42, 27791): 208.23998912749013, (42, 27795): 210.17259234897813, (42, 27801): 208.12798979016475, (42, 27813): 212.0005796433088, (42, 27816): 211.15070363531348, (42, 27823): 208.04630814267264, (42, 27830): 210.12527811925088, (42, 27884): 184.27332005749125, (42, 27885): 189.19736835581438, (42, 27896): 186.20349531439118, (42, 27919): 185.96777415690778, (42, 27922): 186.62559484243295, (42, 27930): 184.98247074242136, (42, 27934): 185.19818964575515, (42, 27935): 185.36845579035025, (42, 27948): 210.7896001804013, (42, 27951): 211.5122609172811, (42, 28061): 193.63558741176234, (42, 28290): 236.5626589789137, (42, 28292): 237.45192185536325, (42, 28293): 236.7364110557468, (42, 28295): 236.36695227284042, (42, 28296): 236.51943171844493, (42, 28297): 236.08977677189452, (42, 28302): 235.77959196523432, (42, 28310): 248.63973432946855, (42, 28313): 249.16949260434566, (42, 28372): 249.5705884564368, (42, 28398): 249.62025793460373, (42, 28399): 249.3159519600447, (42, 28400): 249.7735305691886, (42, 28401): 248.6071379246789, (42, 28445): 248.65674418377145, (42, 28475): 247.87645813068022, (42, 28885): 17.246576288039396, (42, 28886): 17.833667067106763, (42, 28915): 18.714773159578904, (42, 28916): 18.594625711436127, (42, 28917): 19.00662241516842, (42, 28921): 16.426841745981303, (42, 28931): 16.809420860594525, (42, 28945): 22.251357151273638, (42, 28982): 20.551874693645775, (42, 29219): 26.35928419195944, (42, 29228): 26.897731483431823, (42, 29246): 29.728644821950375, (42, 29248): 31.29388686488523, (42, 29282): 30.574852044411735, (42, 29290): 28.343148656635233, (42, 29291): 28.674631255228665, (42, 29292): 28.59078483454528, (42, 29293): 28.330216737054144, (42, 29294): 29.20558433871349, (42, 29298): 28.766122634630484, (42, 29299): 29.169063218822636, (42, 29304): 28.019474371454812, (42, 29317): 27.056097849291106, (42, 29323): 26.94297443696227, (42, 29330): 27.44586806310594, (42, 29331): 27.361969423828697, (42, 29344): 29.257734643938623, (42, 29445): 43.9668410851657, (42, 29724): 307.7033650835687, (42, 29738): 308.0629578350093, (42, 29745): 306.92744651556905, (42, 29748): 306.6937618970358, (42, 29750): 307.09465742513567, (42, 29759): 306.25506422067576, (42, 29772): 307.5769733091845, (42, 29781): 307.2756577918775, (42, 29784): 307.2387115487061, (42, 29790): 307.48553460336353, (42, 29811): 306.5361229099007, (42, 29817): 307.8081213702183, (42, 29818): 307.50663533732, (42, 29929): 307.0744757010147, (42, 30039): 312.9457158661624, (42, 30066): 310.58669677363145, (42, 30116): 297.46687407668594, (42, 30238): 278.0623251071908, (42, 30248): 288.8222979284978, (42, 30260): 289.1425531258219, (42, 30545): 19.585148016087047, (42, 30733): 37.676077084597914, (42, 30756): 44.18403386469646, (42, 30921): 34.41111206244404, (42, 31079): 90.12133581017271, (42, 31149): 89.6039307069109, (42, 31154): 89.9753390670015, (42, 31160): 89.67726744587985, (42, 31163): 90.22973985201358, (42, 31189): 96.29083443995367, (42, 31215): 96.24949650211478, (42, 31259): 98.80965514668759, (42, 31262): 99.35360246847867, (42, 31430): 91.03439591695687, (42, 31568): 112.08162994802615, (42, 31751): 94.55806006789587, (43, 109): 189.07797601070138, (43, 872): 12.5, (43, 873): 12.5, (43, 877): 12.5, (43, 879): 12.5, (43, 884): 12.5, (43, 889): 12.5, (43, 891): 12.5, (43, 892): 12.5, (43, 894): 12.5, (43, 896): 12.5, (43, 903): 12.5, (43, 909): 12.5, (43, 910): 12.5, (43, 912): 12.5, (43, 913): 12.5, (43, 916): 12.5, (43, 926): 12.5, (43, 927): 12.5, (43, 948): 12.5, (43, 961): 12.5, (43, 962): 12.5, (43, 963): 12.5, (43, 967): 12.5, (43, 974): 12.5, (43, 998): 12.5, (43, 1014): 20.4949604636942, (43, 1086): 13.3267576804748, (43, 1087): 14.868774924652321, (43, 1089): 14.490084792694864, (43, 1090): 14.180386391641656, (43, 1092): 13.594507653664449, (43, 1097): 13.739295453656144, (43, 1107): 14.30152798203147, (43, 1387): 146.30826133769892, (43, 1554): 158.6919821704442, (43, 1827): 46.265065666738565, (43, 1828): 46.26146434930706, (43, 1829): 46.47291055139665, (43, 1830): 46.81386773237702, (43, 1831): 46.808688724538634, (43, 1832): 46.66162207431339, (43, 1833): 46.58869335019816, (43, 1836): 46.38788098388904, (43, 1841): 47.10386530668012, (43, 1843): 46.855386828587534, (43, 1844): 47.04935815587508, (43, 1845): 46.82754242284862, (43, 1847): 45.62317100094973, (43, 1848): 45.98305947840057, (43, 1849): 47.75314685181127, (43, 1850): 47.852201580222115, (43, 1851): 46.48344928396929, (43, 1852): 46.706903245386655, (43, 1854): 46.72259636694438, (43, 1856): 45.83093119856067, (43, 1857): 46.064702892050875, (43, 1858): 47.45499062173445, (43, 1861): 46.61472042086017, (43, 1866): 45.979610136287384, (43, 1867): 46.95896862126041, (43, 1868): 46.60368276536109, (43, 1870): 47.27450547089901, (43, 1871): 46.75389074072449, (43, 1875): 46.572067919961604, (43, 1880): 45.877597826199, (43, 1882): 46.262753064102476, (43, 1883): 47.64723210778162, (43, 1889): 45.738211444223076, (43, 1893): 46.184944963103696, (43, 1894): 45.89276268378546, (43, 1899): 45.3974579415492, (43, 1900): 45.50925879679317, (43, 1902): 46.60022405741702, (43, 1905): 47.03050320334506, (43, 1907): 46.01951826979271, (43, 1910): 45.8990989886292, (43, 1917): 47.08635532749418, (43, 1920): 45.87520476624489, (43, 1935): 46.71870365710756, (43, 1937): 47.04162680872095, (43, 1946): 44.445105642402815, (43, 1949): 44.63994262995411, (43, 1950): 44.1001857280615, (43, 1951): 44.460591005046936, (43, 1952): 45.316926366132115, (43, 1953): 45.018505460195016, (43, 1954): 45.122714838849916, (43, 1958): 44.756523254767856, (43, 1960): 45.362519471822, (43, 1968): 45.60066196413797, (43, 1969): 46.43084980314822, (43, 1974): 46.24155335930617, (43, 1975): 46.355470009001486, (43, 1979): 45.447300847696404, (43, 1980): 45.74867223326445, (43, 1981): 45.72189787995154, (43, 1985): 45.78700563344327, (43, 1994): 44.59846285779286, (43, 2011): 46.38355709740083, (43, 2019): 49.28758755024011, (43, 2020): 48.90642282904932, (43, 2029): 47.84638944410941, (43, 2030): 48.63606008937587, (43, 2032): 47.877499376445755, (43, 2033): 48.24000115305362, (43, 2034): 48.42739584042188, (43, 2036): 48.15882212882078, (43, 2037): 48.18856261820522, (43, 2038): 47.33905565894446, (43, 2042): 51.11071583177522, (43, 2050): 47.786455209002895, (43, 2051): 47.942198351620405, (43, 2053): 47.949648763412114, (43, 2054): 48.29037218991642, (43, 2066): 47.6341559489348, (43, 2067): 47.52863992094073, (43, 2071): 43.868673768232185, (43, 2072): 44.32705568445415, (43, 2073): 42.12284361239896, (43, 2074): 42.16867089216627, (43, 2080): 41.470490872186346, (43, 2082): 44.62156658922083, (43, 2083): 44.848140696247306, (43, 2089): 44.04108777263931, (43, 2090): 44.21966593690998, (43, 2092): 43.711336140863196, (43, 2098): 41.59535465021925, (43, 2099): 42.06728497788372, (43, 2101): 41.71328321818508, (43, 2102): 43.11489518269715, (43, 2103): 42.74552792340155, (43, 2104): 42.63084064942245, (43, 2106): 45.13708930710463, (43, 2112): 42.0694754412369, (43, 2113): 43.42480782275982, (43, 2114): 44.07394337812608, (43, 2117): 45.508357739359276, (43, 2123): 37.87895202329435, (43, 2124): 38.202985244361436, (43, 2134): 37.51555865718715, (43, 2138): 38.3681914260742, (43, 2141): 37.552386161528545, (43, 2148): 39.102887779374356, (43, 2150): 36.814193700802896, (43, 2151): 37.223616409985176, (43, 2152): 36.70325877493339, (43, 2153): 39.09268627723162, (43, 2154): 37.71267886269409, (43, 2155): 37.77522741164254, (43, 2156): 37.38049007981582, (43, 2157): 38.53555135757019, (43, 2160): 39.285830640366285, (43, 2161): 36.748210946272096, (43, 2162): 39.62568376361125, (43, 2163): 39.14376119690208, (43, 2164): 39.1954384233967, (43, 2168): 37.481388345692594, (43, 2172): 38.32664903622371, (43, 2174): 37.310906064886716, (43, 2178): 38.75614663606038, (43, 2179): 38.604171605737655, (43, 2183): 38.452446691225006, (43, 2185): 38.53134922543145, (43, 2186): 38.243180114557475, (43, 2190): 39.23630377895907, (43, 2192): 38.73770864766224, (43, 2193): 38.51060859364903, (43, 2194): 38.00197107296814, (43, 2195): 38.05380482303787, (43, 2197): 38.912958319933345, (43, 2205): 38.39957733237836, (43, 2207): 37.700695443621186, (43, 2208): 38.11954468853781, (43, 2212): 38.40431554236503, (43, 2214): 31.168090615714643, (43, 2225): 32.95344862959495, (43, 2231): 26.95853404224033, (43, 2278): 39.198301165468685, (43, 2284): 40.573782805972144, (43, 2285): 40.607105114255845, (43, 2291): 39.89732670591411, (43, 2292): 38.67304916842267, (43, 2307): 39.97955126924872, (43, 2313): 40.14757457924885, (43, 2317): 37.413535748952256, (43, 2319): 39.13947822846229, (43, 2321): 39.8094094534668, (43, 2323): 39.36547476086573, (43, 2326): 40.38680796896286, (43, 2327): 39.960214160562266, (43, 2329): 39.706284729465175, (43, 2330): 39.503315557548135, (43, 2332): 40.373995555205575, (43, 2344): 38.7703075363406, (43, 2346): 39.00155353085774, (43, 2361): 36.89265867287199, (43, 2368): 43.00249514053373, (43, 2374): 43.65295286459562, (43, 2375): 43.70137324626913, (43, 2377): 41.86280622772689, (43, 2378): 44.0990792655873, (43, 2379): 44.36836581395116, (43, 2380): 44.37289529072661, (43, 2383): 42.176546142874514, (43, 2385): 42.36052300072762, (43, 2395): 42.198837375266294, (43, 2397): 44.272806947625625, (43, 2398): 41.30197145140882, (43, 2399): 41.80798524729868, (43, 2400): 41.66673119852397, (43, 2402): 43.26543076591088, (43, 2403): 43.65929977486582, (43, 2404): 43.66637376241722, (43, 2405): 42.80210840312004, (43, 2407): 43.37026989348374, (43, 2408): 43.929664579505406, (43, 2409): 43.02794040933798, (43, 2411): 44.04766021268686, (43, 2412): 43.796270200301194, (43, 2413): 44.17290013262844, (43, 2414): 43.70243805872713, (43, 2422): 44.06760565534364, (43, 2424): 43.821386284404866, (43, 2426): 43.8275237829115, (43, 2433): 43.25053562848631, (43, 2436): 43.31783460517768, (43, 2437): 40.96960669632416, (43, 2440): 41.41463170192744, (43, 2445): 53.69301104073177, (43, 2447): 52.22096476219889, (43, 2454): 53.36757909128922, (43, 2455): 53.22696611715729, (43, 2460): 49.94605994048847, (43, 2461): 50.395298758567506, (43, 2471): 58.627166042645705, (43, 2492): 61.32776783213894, (43, 2511): 56.297295643383904, (43, 2523): 58.90986466332992, (43, 2525): 59.05194283775931, (43, 2535): 54.16559171456969, (43, 2537): 53.609888554627425, (43, 2538): 53.73382533391648, (43, 2539): 54.82132549973704, (43, 2540): 54.4518135502748, (43, 2542): 55.30272350478996, (43, 2559): 63.03543396434268, (43, 2575): 63.413810845084456, (43, 2599): 44.75418176185873, (43, 2600): 48.96104672571948, (43, 2607): 45.63287444489973, (43, 2627): 63.32563170130201, (43, 2647): 66.08503319612703, (43, 2674): 63.583928492590786, (43, 2681): 64.11468823811063, (43, 2683): 64.62301135302302, (43, 2686): 63.261365553070895, (43, 2689): 75.74922122154985, (43, 2690): 75.9809776324592, (43, 2713): 83.59833870018147, (43, 2714): 84.53685065425051, (43, 2715): 84.7895828006621, (43, 2739): 84.34689164769917, (43, 2740): 80.68865512339586, (43, 2741): 80.67076589719733, (43, 2749): 84.78139283636892, (43, 2750): 84.59560955831807, (43, 2752): 84.65596388348119, (43, 2755): 85.02340845528184, (43, 2758): 85.18701949396296, (43, 2759): 85.06904219072577, (43, 2769): 84.47264206592767, (43, 2771): 81.63621159682164, (43, 2779): 83.63712505761198, (43, 2784): 81.63967094811122, (43, 2800): 84.11609679913211, (43, 2802): 81.21046438926362, (43, 2803): 80.87131109167575, (43, 2804): 80.603055544228, (43, 2805): 82.1576598684599, (43, 2807): 81.896409446434, (43, 2809): 82.34851456192423, (43, 2812): 80.07626770456952, (43, 2814): 83.9025791705112, (43, 2817): 86.20760776596705, (43, 2819): 81.33260700738327, (43, 2823): 82.39414996028204, (43, 2832): 82.82623260120907, (43, 2836): 81.63017526229018, (43, 2839): 81.6445970825663, (43, 2841): 85.12005968289151, (43, 2843): 84.63174699800064, (43, 2846): 82.86604657918218, (43, 2849): 83.42765857309146, (43, 2852): 82.99828974775484, (43, 2853): 83.64046396574082, (43, 2876): 84.91100760765907, (43, 2877): 86.03799027579258, (43, 2885): 88.68355819928726, (43, 2918): 79.92614880383229, (43, 2921): 80.63669389344233, (43, 2925): 76.53370513218927, (43, 2926): 74.72923826985901, (43, 2930): 80.05114359540289, (43, 2931): 77.37427901505549, (43, 2938): 80.34864998760578, (43, 2940): 79.6591197810662, (43, 2947): 77.66367327763204, (43, 2949): 79.0880468302441, (43, 2950): 79.69138601351989, (43, 2952): 79.4929358595094, (43, 2958): 79.28188906343131, (43, 2959): 79.00937772529477, (43, 2960): 79.64001291212428, (43, 2961): 79.60126960766742, (43, 2963): 79.3431355834511, (43, 2968): 79.72315747952048, (43, 2976): 79.03606527850792, (43, 2981): 78.24608848102662, (43, 2982): 78.66257641624459, (43, 2984): 78.59381984252816, (43, 3003): 78.84564695460011, (43, 3046): 70.40696847182663, (43, 3050): 75.17438295046212, (43, 3051): 75.12901633631382, (43, 3053): 74.92451604122496, (43, 3069): 78.14730862637141, (43, 3071): 73.64181778934929, (43, 3080): 89.54724833010928, (43, 3199): 81.5101895211561, (43, 3200): 81.47069890037677, (43, 3205): 83.69134580564248, (43, 3209): 81.74297658408604, (43, 3215): 81.19597283493057, (43, 3217): 80.78317123294883, (43, 3249): 80.91922963974233, (43, 3263): 84.04190950687658, (43, 3289): 81.08924424296977, (43, 3301): 81.95837758104929, (43, 3302): 81.52188860647128, (43, 3307): 81.24911198179194, (43, 3310): 82.14329204809547, (43, 3391): 97.67327314562034, (43, 3509): 76.48960412973207, (43, 3510): 76.88565039381375, (43, 3511): 76.38669326842594, (43, 3512): 76.42962528884829, (43, 3514): 76.16248120846117, (43, 3519): 76.76427162132718, (43, 3536): 75.37497124476381, (43, 3545): 74.51378205655142, (43, 3548): 74.8179260893883, (43, 3572): 75.43978391883685, (43, 3581): 76.71881607256499, (43, 3583): 76.00253033828665, (43, 3601): 76.4407494845177, (43, 3656): 78.03253852755371, (43, 3669): 80.92339809406003, (43, 3670): 80.69586594002548, (43, 3695): 81.65776535404311, (43, 3696): 81.3573723813853, (43, 3782): 70.94759382154663, (43, 3792): 71.94439400220472, (43, 3989): 284.9956769418203, (43, 4008): 287.742195530631, (43, 4031): 287.54170561092883, (43, 4045): 286.58840726348274, (43, 4144): 286.7521504588541, (43, 4145): 283.9994086818183, (43, 4164): 285.69311773625446, (43, 4168): 284.8390203887413, (43, 4173): 284.6649186956601, (43, 4181): 282.9876381878157, (43, 4228): 281.39562933351664, (43, 4248): 280.713036287848, (43, 4254): 265.4457033318675, (43, 4260): 265.53231675797065, (43, 4262): 266.4916530041431, (43, 4273): 266.2977941542662, (43, 4319): 256.77138928283244, (43, 4326): 256.47431829895726, (43, 4328): 256.6120833944428, (43, 4334): 257.1524420892925, (43, 4335): 256.9167552547752, (43, 4372): 231.87025763160167, (43, 4413): 238.81138689965832, (43, 4434): 231.75655710704882, (43, 4447): 233.38853336526435, (43, 4452): 231.76416712871938, (43, 4463): 211.97612593265748, (43, 4465): 212.76709245417058, (43, 4619): 237.68609969060384, (43, 4645): 239.90094961752982, (43, 4657): 239.34207113370442, (43, 4666): 238.37224883829822, (43, 4676): 239.70508526945903, (43, 4678): 240.12571834907837, (43, 4689): 238.90799810636383, (43, 4704): 245.48354704097832, (43, 4726): 255.70477411031862, (43, 4727): 255.48914681369436, (43, 4730): 255.0907311641028, (43, 4731): 255.07606386335567, (43, 4734): 256.04894524347526, (43, 4735): 255.73375604504537, (43, 4736): 255.74038067553295, (43, 4737): 255.24690496698435, (43, 4738): 255.217349406841, (43, 4756): 255.37367895411674, (43, 4760): 254.83719970277852, (43, 4761): 255.17786793998982, (43, 4762): 254.41011774048542, (43, 4765): 254.87773283277153, (43, 4773): 256.2375231417743, (43, 4774): 255.85861038727475, (43, 4790): 256.1219688676818, (43, 4795): 255.98008960677055, (43, 4799): 255.85335173383504, (43, 4801): 256.05128286268274, (43, 4804): 256.28656943775445, (43, 4805): 256.16730592622076, (43, 4806): 255.50201121329775, (43, 4815): 255.13119305333728, (43, 4816): 255.75712671676024, (43, 4817): 255.64996263003948, (43, 4826): 255.39334917649148, (43, 4830): 254.99487491395115, (43, 4839): 255.45382516736666, (43, 4840): 255.55424364798793, (43, 4841): 255.02547967405673, (43, 4846): 254.9124065689182, (43, 4848): 254.67839625922213, (43, 4850): 254.84263767915868, (43, 4871): 253.19647277316426, (43, 4883): 254.86426312169604, (43, 4900): 254.2660421394412, (43, 4901): 253.85102210869758, (43, 4917): 233.9243931052584, (43, 4931): 232.1521588911344, (43, 4944): 234.2666896246288, (43, 4956): 232.3357132716675, (43, 4958): 232.00507587470835, (43, 4959): 231.47717761311387, (43, 4961): 232.80862231444985, (43, 4966): 231.7407716694815, (43, 5207): 229.7505157364601, (43, 5272): 206.3068594987688, (43, 5283): 206.81258817313577, (43, 5287): 206.9287631807186, (43, 5289): 207.1262597050159, (43, 5293): 207.08238800873957, (43, 5295): 208.59775177422247, (43, 5296): 208.16367132601334, (43, 5298): 207.90962360154643, (43, 5303): 207.99786254992966, (43, 5305): 205.16842864904098, (43, 5306): 204.14520994277544, (43, 5307): 204.85296461444955, (43, 5308): 205.2772259187638, (43, 5313): 205.79155621705985, (43, 5314): 206.29187998321655, (43, 5317): 205.00270707069706, (43, 5319): 207.3710316658131, (43, 5324): 207.38814958088366, (43, 5326): 207.4245514896441, (43, 5348): 203.65274743569202, (43, 5351): 203.45438891066553, (43, 5399): 206.81679412206637, (43, 5413): 203.20443001378945, (43, 5422): 207.53213397023737, (43, 5445): 206.09269492237354, (43, 5448): 205.56543721605206, (43, 5456): 204.99155442696681, (43, 5467): 205.3625058341207, (43, 5624): 201.07859189131142, (43, 5671): 223.87591316546394, (43, 5672): 223.19521806319244, (43, 5797): 232.4251751433543, (43, 5871): 210.48347676050085, (43, 5976): 203.86699606515592, (43, 6118): 82.48247663932746, (43, 6248): 95.92710674788457, (43, 6345): 186.624304152081, (43, 6352): 184.7076766419738, (43, 6354): 186.99748966247375, (43, 6359): 187.55022523227922, (43, 6376): 185.446390446237, (43, 6378): 186.78898081120954, (43, 6381): 187.51345948207074, (43, 6383): 186.14707569128095, (43, 6396): 187.9944311935013, (43, 6399): 186.85911614378958, (43, 6408): 184.5996283733043, (43, 6409): 185.044454067996, (43, 6419): 181.21345588196243, (43, 6422): 184.487555992436, (43, 6423): 184.3065837079333, (43, 6424): 186.30102288322232, (43, 6439): 185.7852316204733, (43, 6464): 185.10865038055093, (43, 6465): 185.06863666742254, (43, 6469): 185.6377294623476, (43, 6470): 185.59575985346837, (43, 6472): 188.27033900923973, (43, 6480): 187.1258126934498, (43, 6486): 187.535463533541, (43, 6497): 187.35640616440068, (43, 6503): 184.36950172935917, (43, 6508): 184.9712729787665, (43, 6509): 185.13890883818686, (43, 6521): 187.04544825943003, (43, 6544): 186.46957186394405, (43, 6552): 184.02678985224736, (43, 6553): 183.6759572096246, (43, 6554): 183.32511091740005, (43, 6578): 184.67902253427275, (43, 6582): 183.961325251477, (43, 6601): 184.73895196820007, (43, 6609): 187.94577607129656, (43, 6610): 187.94281228971366, (43, 6611): 188.26486908055688, (43, 6614): 188.24439481099049, (43, 6615): 188.21619437094674, (43, 6616): 188.23349272710044, (43, 6617): 188.19654479536604, (43, 6618): 188.35792981713914, (43, 6619): 187.94942710982636, (43, 6620): 188.08350486142618, (43, 6621): 187.76612416467336, (43, 6622): 187.941703828793, (43, 6623): 188.03924943440367, (43, 6624): 187.6189845727003, (43, 6625): 187.65129874937026, (43, 6626): 188.00372478668066, (43, 6627): 188.31515813593498, (43, 6628): 187.86509791556247, (43, 6629): 187.5038836515546, (43, 6630): 187.66340640989586, (43, 6632): 187.56234221621813, (43, 6634): 187.2531386652416, (43, 6635): 187.7484827254664, (43, 6636): 188.1949703032862, (43, 6637): 187.09475640905492, (43, 6638): 187.54531645842198, (43, 6639): 188.2505158575265, (43, 6640): 187.67427201396967, (43, 6641): 187.6362895017015, (43, 6642): 187.44550638288698, (43, 6643): 188.0863481072504, (43, 6645): 187.91640337290517, (43, 6646): 188.37850005105932, (43, 6647): 187.5903467139435, (43, 6653): 188.25263691889037, (43, 6655): 188.3060678636173, (43, 6658): 187.16927240676517, (43, 6662): 187.31524032561992, (43, 6819): 168.89802457820082, (43, 6996): 172.29699869268836, (43, 7059): 176.2925389368093, (43, 7187): 165.59045938591697, (43, 7304): 159.15030298063874, (43, 7528): 170.1553420951189, (43, 7720): 195.4367154114005, (43, 7793): 194.35297656662928, (43, 7807): 194.87176340437694, (43, 7808): 194.10097802281217, (43, 7831): 188.98330574368063, (43, 7850): 193.44520151324474, (43, 7852): 192.8039352630011, (43, 8012): 195.18149034576732, (43, 8125): 194.75461507772235, (43, 8208): 202.73646953271532, (43, 8392): 189.70514687447127, (43, 8651): 150.12008553010915, (43, 9088): 170.92160035303436, (43, 9443): 133.35040126688028, (43, 9444): 133.83731859194995, (43, 9828): 113.09898143221653, (43, 9868): 114.99415525658854, (43, 10180): 194.92851900685636, (43, 10256): 205.20188318572923, (43, 10276): 200.8508978250179, (43, 10378): 203.52304444430632, (43, 10676): 189.5816862886835, (43, 10714): 182.22383019983084, (43, 10730): 184.8330748435149, (43, 10862): 169.12046171935987, (43, 10881): 170.7568246835821, (43, 10883): 170.49494557990846, (43, 10885): 168.7893002245275, (43, 10891): 170.08863669318995, (43, 10909): 170.13619628829636, (43, 10911): 170.5630400301201, (43, 10913): 170.12166409143163, (43, 10915): 170.20667883307527, (43, 10919): 170.52001329226, (43, 11037): 157.147700212277, (43, 11039): 153.88230311415452, (43, 11516): 313.5037459919914, (43, 11856): 257.4112539039231, (43, 11857): 256.8535862655672, (43, 11861): 257.14376465833567, (43, 11881): 256.8958968418466, (43, 11902): 255.04538580286797, (43, 11911): 254.86712771744612, (43, 11914): 255.05590426552794, (43, 11922): 256.3764844122998, (43, 11924): 256.8529402838611, (43, 11926): 256.3291599428816, (43, 11950): 257.5514883526609, (43, 11963): 259.2685707999728, (43, 11983): 258.35289032848016, (43, 11985): 260.11643225388906, (43, 12009): 259.99944228901455, (43, 12010): 258.72613647759084, (43, 12018): 258.9567751550417, (43, 12020): 259.2565156383694, (43, 12021): 259.48279107799755, (43, 12024): 260.6499371212093, (43, 12025): 260.2106605524381, (43, 12027): 259.94538418559085, (43, 12031): 258.52062083551516, (43, 12032): 258.8919687276112, (43, 12035): 259.97174773488626, (43, 12041): 260.1321554696795, (43, 12045): 244.12680791397952, (43, 12145): 251.8421017729978, (43, 12275): 286.18840420108063, (43, 12294): 283.2143841927766, (43, 12358): 293.1233122770481, (43, 12463): 297.0798691046942, (43, 12465): 296.97814183830036, (43, 12482): 298.4675556107531, (43, 12503): 298.2790976223483, (43, 12506): 298.7245127667807, (43, 12549): 297.56125468070405, (43, 12559): 297.2617182134105, (43, 12569): 297.69746490733223, (43, 12572): 298.0282108557251, (43, 12574): 297.3150324970244, (43, 12576): 297.9237557402591, (43, 12591): 297.7268387367735, (43, 12608): 300.33754879211153, (43, 12696): 295.9374203170277, (43, 12710): 298.30356940780405, (43, 12728): 297.24341628522774, (43, 12766): 223.78752481095037, (43, 12771): 219.85117925538424, (43, 12790): 219.41861402144073, (43, 12795): 218.49638042575492, (43, 12797): 213.77140018495436, (43, 12798): 214.35029913220782, (43, 12811): 217.87945334608796, (43, 12830): 216.80399894359823, (43, 12848): 217.20261694008548, (43, 12850): 217.37061022151588, (43, 12852): 216.57144175340662, (43, 12854): 216.0321599686826, (43, 12859): 217.68282834138196, (43, 12861): 214.89886524572054, (43, 12865): 218.63662701885974, (43, 12866): 218.2954093242456, (43, 12867): 219.43268550111935, (43, 12874): 218.8899623434992, (43, 12875): 219.27055629761765, (43, 12881): 217.6713768518053, (43, 12883): 218.33051615562957, (43, 12885): 219.63905109324932, (43, 12888): 217.97932702336718, (43, 12889): 217.78701572491042, (43, 12892): 219.03017788616089, (43, 12893): 218.0478682218408, (43, 12896): 218.32427724743812, (43, 12906): 219.123151082713, (43, 13018): 215.58055240688304, (43, 13071): 215.9402002666672, (43, 13131): 210.48641003539868, (43, 13146): 213.75344829947505, (43, 13159): 210.50523499540455, (43, 13193): 209.71855185622823, (43, 13198): 203.06970271936342, (43, 13292): 209.99757244629154, (43, 13296): 211.51078194284588, (43, 13406): 200.14566092172987, (43, 13407): 200.02137866662736, (43, 13417): 200.17799226647335, (43, 13418): 200.93693876249424, (43, 13438): 203.1170093886586, (43, 13442): 203.44579006180854, (43, 13443): 202.95856375108906, (43, 13764): 166.2420084431395, (43, 13766): 166.83077950209187, (43, 13771): 166.6867765267268, (43, 13783): 165.03838009765138, (43, 13784): 167.2902810169783, (43, 13792): 166.21715104534246, (43, 13824): 164.71776251044824, (43, 14017): 165.8693793959709, (43, 14870): 173.3326010353824, (43, 14997): 162.3180639528086, (43, 15000): 162.32429873410248, (43, 15003): 162.71030198997818, (43, 15006): 163.96144054379363, (43, 15007): 164.39967427192502, (43, 15056): 164.1611990584835, (43, 15063): 163.72954554010596, (43, 15069): 163.51913212592248, (43, 15076): 164.42517486687544, (43, 15086): 163.11150961913813, (43, 15087): 162.53946519331205, (43, 15111): 161.271089917436, (43, 15116): 161.99179408416964, (43, 15722): 150.3145641984344, (43, 15998): 140.89660341315596, (43, 16073): 113.11108224172047, (43, 16939): 32.114323511305756, (43, 16940): 31.604997842918635, (43, 16951): 33.44235726680378, (43, 16963): 33.1802093099527, (43, 16965): 33.25734458850683, (43, 16969): 33.88943996447599, (43, 16970): 32.96221613453767, (43, 16971): 32.85546266435212, (43, 16973): 33.304173859156585, (43, 16974): 33.72308673744405, (43, 16976): 32.68595079351225, (43, 16978): 32.445123262223305, (43, 16980): 32.34911353931458, (43, 16982): 34.19003551869491, (43, 17045): 77.50300362930301, (43, 17048): 78.05160085789504, (43, 17304): 276.708759602131, (43, 17305): 276.29580838077874, (43, 17330): 276.72180756428304, (43, 17334): 275.7931532164079, (43, 17343): 277.41138738905124, (43, 17345): 275.81474521677615, (43, 17347): 276.69369777314165, (43, 17351): 274.56258988721885, (43, 17372): 275.71314545069623, (43, 17373): 277.3499508142599, (43, 17377): 277.46925086174065, (43, 17382): 276.414994372767, (43, 17383): 276.5928111322609, (43, 17389): 275.97489015811806, (43, 17400): 277.03931815506814, (43, 17401): 277.00959385641505, (43, 17402): 277.10694257159486, (43, 17403): 277.2164682114438, (43, 17440): 275.9356753338021, (43, 17455): 277.26163805553244, (43, 17491): 277.3998989994283, (43, 17507): 275.02365998649265, (43, 17509): 275.5928146138243, (43, 17590): 274.2317776028317, (43, 17615): 270.59548464127283, (43, 17642): 271.21585167414463, (43, 17643): 271.18994538696035, (43, 17668): 270.55562286585507, (43, 17721): 269.02387533893415, (43, 17754): 274.5024956042581, (43, 17769): 275.1466456419657, (43, 17776): 272.92895747558214, (43, 17804): 276.0859495094504, (43, 17809): 276.67311008095146, (43, 17824): 276.24982588335473, (43, 17837): 274.7283630719686, (43, 17838): 274.82407795193643, (43, 17862): 274.4026062329115, (43, 17866): 275.6366263205983, (43, 17872): 273.9623469984405, (43, 17873): 273.0267101334202, (43, 17881): 274.46692411297795, (43, 17947): 42.28731021072332, (43, 17951): 43.50741025328343, (43, 17953): 43.76541099856406, (43, 17954): 43.69836301592502, (43, 17959): 42.495111677736595, (43, 17963): 42.90615791626766, (43, 18000): 49.31497892587628, (43, 18001): 49.05211000121426, (43, 18111): 40.875516235923726, (43, 18148): 66.12152035380349, (43, 18166): 56.431851239059576, (43, 18189): 46.147499444752775, (43, 18239): 277.6279572810613, (43, 18240): 277.62365055909703, (43, 18245): 277.68428847648335, (43, 18247): 277.5585414341712, (43, 18251): 277.6853239917186, (43, 18256): 277.8258033746529, (43, 18258): 277.6798195173186, (43, 18259): 277.70776789188244, (43, 18260): 277.766946136858, (43, 18262): 277.8775720437676, (43, 18263): 277.8659635886605, (43, 18264): 277.9246701801107, (43, 18266): 277.9235106921893, (43, 18267): 277.9805599285493, (43, 18268): 278.0095186492601, (43, 18269): 278.1234350660097, (43, 18275): 278.06970537254756, (43, 18285): 277.90369645117863, (43, 18308): 276.7018016422659, (43, 18313): 276.30193971635043, (43, 18314): 276.49353535631445, (43, 18315): 278.1108666313483, (43, 18316): 278.1047822032912, (43, 18317): 278.1582781496321, (43, 18320): 278.20394817960306, (43, 18321): 278.23483044070565, (43, 18322): 278.3184636006143, (43, 18324): 278.38200719897856, (43, 18325): 278.6376614752401, (43, 18326): 278.54226374634663, (43, 18327): 278.209909980238, (43, 18329): 278.74882718128254, (43, 18330): 278.6310486839352, (43, 18331): 278.4584040491732, (43, 18332): 278.28220799410013, (43, 18333): 278.6015775567851, (43, 18336): 278.45325555002853, (43, 18337): 278.53800193270325, (43, 18403): 278.4263083519036, (43, 18432): 275.0082395772256, (43, 18451): 277.3302208655042, (43, 18466): 279.5591740344505, (43, 18481): 278.1680708545416, (43, 18483): 278.1706595404959, (43, 18484): 278.0278828628944, (43, 18485): 277.5947960665065, (43, 18486): 277.9611318235113, (43, 18487): 277.62971799513207, (43, 18489): 277.9325039620439, (43, 18490): 278.25075417405543, (43, 18491): 278.40485915804567, (43, 18492): 277.3031528880483, (43, 18493): 277.90238854814726, (43, 18494): 277.8723646390361, (43, 18495): 278.1354330667732, (43, 18496): 277.9765486910477, (43, 18497): 277.55020884261864, (43, 18498): 277.6390546059396, (43, 18499): 277.880319647878, (43, 18501): 277.6998571476145, (43, 18502): 277.5450595929678, (43, 18503): 277.4303968646934, (43, 18504): 278.04429751915455, (43, 18506): 277.71302904832686, (43, 18507): 277.5633237507043, (43, 18508): 277.84352799595234, (43, 18509): 277.84344141548297, (43, 18510): 277.42957768356814, (43, 18511): 277.9418657691432, (43, 18512): 277.76617725138954, (43, 18515): 278.0542815255029, (43, 18516): 278.0552548551897, (43, 18517): 277.8546104823957, (43, 18518): 278.1857102470557, (43, 18519): 278.07950795900905, (43, 18520): 277.80186880433894, (43, 18522): 278.74052499300853, (43, 18523): 278.77044170047105, (43, 18532): 278.97909533801493, (43, 18535): 278.54193698692853, (43, 18537): 278.29851327527035, (43, 18539): 278.3475267441893, (43, 18540): 278.3738434750324, (43, 18541): 278.49196800449937, (43, 18542): 278.56730952763434, (43, 18543): 278.1914755188061, (43, 18546): 278.3636091141304, (43, 18555): 278.74471866287985, (43, 18556): 278.811378712546, (43, 18565): 278.94567595756575, (43, 18567): 279.04929628653014, (43, 18568): 278.84482727471817, (43, 18577): 280.3370577200549, (43, 18583): 280.0978418030483, (43, 18605): 280.4246822513792, (43, 18608): 279.1609491621835, (43, 18616): 281.81721547795223, (43, 18618): 282.9942250425534, (43, 18625): 282.6197252404201, (43, 18645): 281.5829785582591, (43, 18646): 281.847191731741, (43, 18653): 280.8288127417829, (43, 18654): 281.7819020950559, (43, 18655): 281.1491706795686, (43, 18666): 285.05393596312797, (43, 18837): 281.05212915549123, (43, 18974): 277.3781214599728, (43, 18999): 278.4149181794108, (43, 19000): 278.77657420118476, (43, 19174): 261.87906270366085, (43, 19342): 269.3418926073927, (43, 19455): 264.3276528546171, (43, 19555): 246.83977197012769, (43, 19564): 248.29286803503723, (43, 19573): 247.4375765925176, (43, 19586): 247.0307451555832, (43, 19605): 247.2585864651795, (43, 19611): 247.822060648132, (43, 19614): 247.46083903858502, (43, 19641): 256.4053298267925, (43, 19702): 256.36671095619937, (43, 19713): 255.68826538047264, (43, 19731): 243.3019265847367, (43, 19819): 261.81472402302484, (43, 19893): 234.46962882387683, (43, 19899): 237.70536822882335, (43, 19929): 235.51540084550052, (43, 19951): 242.67160689006326, (43, 19962): 235.72430458383388, (43, 19970): 238.05852672397728, (43, 19971): 237.91555068718003, (43, 19972): 237.18303104079945, (43, 19975): 237.02223254274543, (43, 19978): 244.99953612953234, (43, 19987): 245.24449907697743, (43, 19989): 243.25584819509388, (43, 20039): 245.6694514856508, (43, 20043): 246.66938654133278, (43, 20047): 246.18018020207137, (43, 20052): 243.84228720346516, (43, 20054): 243.93624933747913, (43, 20085): 255.08195852865032, (43, 20104): 255.7485556550044, (43, 20132): 251.4999536265822, (43, 20203): 232.4250339047241, (43, 20280): 231.06351972361657, (43, 20285): 230.62724575531325, (43, 20290): 231.521204456398, (43, 20297): 230.88024947261476, (43, 20309): 244.23699535466545, (43, 20453): 255.99957676497417, (43, 20485): 226.79955525419982, (43, 20520): 225.20568749792412, (43, 20526): 223.98704577118244, (43, 20698): 158.615026559481, (43, 20868): 142.27217020348445, (43, 21042): 214.9276393241595, (43, 21057): 219.79963060095187, (43, 21066): 217.25749419157836, (43, 21075): 216.56455767779252, (43, 21093): 215.07926379126422, (43, 21098): 218.22578550988874, (43, 21127): 215.21391110545747, (43, 21130): 216.02736786141608, (43, 21144): 216.09193654018338, (43, 21146): 214.89691217530037, (43, 21147): 216.0715538189658, (43, 21148): 216.84428994128092, (43, 21153): 215.63487308001524, (43, 21293): 222.7082307906577, (43, 21426): 223.42432862675767, (43, 21442): 228.92728288779062, (43, 21451): 229.4485020335524, (43, 21466): 226.05959369556854, (43, 21469): 226.78036781596265, (43, 21471): 225.6982880036805, (43, 21473): 226.27065949170142, (43, 21475): 225.73273968867488, (43, 21482): 227.31312647613416, (43, 21484): 227.12224655212535, (43, 21488): 226.72075771335, (43, 21494): 225.6202551158806, (43, 21498): 226.18510490789114, (43, 21500): 225.20586110158337, (43, 21514): 226.30704631033183, (43, 21537): 224.8064770977298, (43, 21662): 226.69521612205085, (43, 21691): 223.76584126142464, (43, 21757): 219.37374429617304, (43, 21777): 204.8741376491802, (43, 21778): 204.13430668473535, (43, 21779): 204.44115320070105, (43, 21790): 205.82231089687156, (43, 21802): 205.57513315207626, (43, 21824): 206.23931350137028, (43, 21874): 204.50288353746345, (43, 21879): 203.87245077947455, (43, 21983): 208.0686005803095, (43, 22002): 215.33207457043468, (43, 22132): 212.78094450939986, (43, 22261): 107.39199215936276, (43, 22298): 109.16148745043029, (43, 22339): 101.54934976625694, (43, 22508): 121.82080673457786, (43, 22841): 131.12516677381214, (43, 22842): 130.80889218605594, (43, 22874): 128.72669945635735, (43, 22941): 129.91414453575982, (43, 22956): 130.24162614053634, (43, 22960): 131.18464833392198, (43, 22968): 127.43892206100898, (43, 22970): 128.23419858581323, (43, 22974): 125.80915596863554, (43, 22980): 126.5339093905218, (43, 23025): 122.5445674465449, (43, 23028): 121.5714220197431, (43, 23081): 118.00674124739375, (43, 23104): 110.0043311695893, (43, 23147): 114.96346781699818, (43, 23298): 238.62329262654762, (43, 23376): 236.45915039936165, (43, 23381): 234.7274068642822, (43, 23529): 239.64960306621276, (43, 23556): 238.45354150882156, (43, 23718): 237.65620294996896, (43, 24001): 251.51054440471364, (43, 24094): 254.81538288248515, (43, 24129): 256.95887266821893, (43, 24174): 252.2382241545245, (43, 24235): 256.82349632429106, (43, 24259): 259.0436868383717, (43, 24260): 258.8639067234586, (43, 24261): 258.4294951106322, (43, 24305): 261.5582223791527, (43, 24306): 261.9370668112014, (43, 24307): 261.33386491905213, (43, 24308): 257.2794999629771, (43, 24498): 267.45554511486756, (43, 24499): 267.4906122215196, (43, 24500): 267.1082882825458, (43, 24668): 265.0429287426556, (43, 24711): 269.8684853465424, (43, 24756): 271.1136548588649, (43, 24788): 271.8002841513229, (43, 24809): 269.2526956320664, (43, 24813): 270.06165705969437, (43, 24821): 269.8019111632613, (43, 24825): 269.9686873552191, (43, 24832): 269.1005893985003, (43, 24833): 269.4746172394693, (43, 24835): 269.83944290837525, (43, 24837): 270.452428722713, (43, 24840): 269.0334548189719, (43, 24841): 269.6304307998363, (43, 24844): 269.03801907278734, (43, 24845): 269.42729192907296, (43, 24846): 269.32654904958923, (43, 24849): 269.52444177816733, (43, 24850): 270.16075780956174, (43, 24863): 265.0477901494633, (43, 24866): 265.72114839167597, (43, 24885): 266.4726748574949, (43, 24886): 266.50384404677646, (43, 24889): 268.06401343677703, (43, 24903): 268.67135708283314, (43, 24909): 266.2956866479384, (43, 24999): 295.3244748201145, (43, 25019): 294.62102032060704, (43, 25028): 294.9195942786235, (43, 25137): 230.35712200371074, (43, 25145): 231.2022919773922, (43, 25208): 239.09371805416916, (43, 25233): 237.8948276357038, (43, 25371): 231.62623555482358, (43, 25377): 229.60903713687355, (43, 25828): 188.15922325053324, (43, 25851): 182.66257960300317, (43, 25874): 188.38069182001004, (43, 25898): 190.33196364008998, (43, 25946): 187.56249931247797, (43, 26047): 199.3739491259341, (43, 26066): 217.64116372670907, (43, 26197): 206.40355157749408, (43, 26212): 165.52903243740263, (43, 26253): 163.27446711583156, (43, 26254): 164.1518597761091, (43, 26257): 164.88243158032262, (43, 26258): 163.71082783451376, (43, 26260): 164.31747832996695, (43, 26266): 163.59128346837932, (43, 26267): 164.28852352679934, (43, 26271): 164.29627689031443, (43, 26304): 172.33163666347176, (43, 26305): 172.31387425743253, (43, 26363): 185.23352685594267, (43, 26441): 113.79186648295286, (43, 26442): 113.78309459622692, (43, 26450): 114.84871033092084, (43, 26459): 115.83760326254121, (43, 26462): 116.09773067811926, (43, 26467): 113.18390030241312, (43, 26471): 113.52251454629413, (43, 26472): 113.47134213633582, (43, 26473): 113.37209778531327, (43, 26476): 112.50098660980223, (43, 26485): 114.88206781669169, (43, 26493): 114.38447526416606, (43, 26524): 116.07486146870643, (43, 26525): 115.93383525686342, (43, 26556): 113.96313698816891, (43, 26560): 114.84360747996969, (43, 26561): 115.65436454204412, (43, 26564): 114.0219041212605, (43, 26569): 115.5482509704656, (43, 26570): 115.50208858880264, (43, 26573): 114.92709646221529, (43, 26581): 114.58455144096294, (43, 26583): 115.03082790638098, (43, 26593): 114.11858519144336, (43, 26837): 112.60258922722691, (43, 26844): 112.1169034637784, (43, 26863): 112.27853907561907, (43, 26893): 110.4723747972181, (43, 26902): 109.7719819332794, (43, 26905): 111.30402313159072, (43, 26912): 110.4999057417083, (43, 26921): 111.46695279111368, (43, 26922): 111.66809090201504, (43, 27212): 131.4172759782686, (43, 27218): 132.93325583844424, (43, 27239): 130.4586342740993, (43, 27257): 130.46723044867912, (43, 27274): 130.09889735230342, (43, 27279): 129.76714963114196, (43, 27282): 130.2259285700134, (43, 27283): 130.84113373067095, (43, 27285): 129.64692271166857, (43, 27286): 129.34817511089577, (43, 27290): 130.55480156173502, (43, 27295): 131.44696414998242, (43, 27300): 130.18381010124244, (43, 27344): 129.5822399872456, (43, 27366): 128.6515859636739, (43, 27383): 128.74353267846269, (43, 27398): 129.2019876852739, (43, 27406): 129.94913164702498, (43, 27407): 130.1497536799345, (43, 27426): 133.54682174086005, (43, 27432): 134.60958089156233, (43, 27460): 134.3096516537807, (43, 27523): 122.28416025213448, (43, 27545): 121.77740688612346, (43, 27602): 110.66171515216146, (43, 27606): 111.1338058239449, (43, 27646): 111.79406428505126, (43, 27667): 109.37949616680412, (43, 27672): 109.58610183034028, (43, 27674): 109.78481908204232, (43, 27688): 110.75315765336217, (43, 27692): 108.79894559817274, (43, 27693): 109.08339627503221, (43, 27705): 108.72642659715608, (43, 27712): 108.2680294451303, (43, 27786): 125.41257320447667, (43, 27790): 131.24029039543967, (43, 27791): 132.04113083771713, (43, 27795): 125.29339289398779, (43, 27801): 129.16528067379136, (43, 27813): 124.63793296685475, (43, 27816): 125.88722503841593, (43, 27823): 129.35801500192505, (43, 27830): 127.33779855877657, (43, 27884): 112.47227598690641, (43, 27885): 112.26861239923494, (43, 27896): 112.52963422757396, (43, 27919): 112.88534102111687, (43, 27922): 112.35678910998608, (43, 27930): 112.84330395933031, (43, 27934): 112.53323748906148, (43, 27935): 112.18354584874568, (43, 27948): 92.93092323562773, (43, 27951): 98.3774206237792, (43, 28061): 76.87064278533403, (43, 28290): 46.0374324768343, (43, 28292): 44.129622087811676, (43, 28293): 45.55054057316901, (43, 28295): 44.856339364522334, (43, 28296): 45.57478280425111, (43, 28297): 46.95285534065202, (43, 28302): 46.30061193309009, (43, 28310): 66.51647279007236, (43, 28313): 68.72406242078966, (43, 28372): 64.23993169554781, (43, 28398): 64.56188176506423, (43, 28399): 64.90064465281198, (43, 28400): 64.9361064116012, (43, 28401): 64.2914546335857, (43, 28445): 70.133831498252, (43, 28475): 61.14226836814153, (43, 28885): 255.23925310902143, (43, 28886): 254.76224301507855, (43, 28915): 254.8117086961852, (43, 28916): 254.5664033061123, (43, 28917): 254.28311543357722, (43, 28921): 256.0539331813816, (43, 28931): 255.865928970903, (43, 28945): 252.85769562613848, (43, 28982): 253.6828328722726, (43, 29219): 254.32555751158395, (43, 29228): 252.6062880707009, (43, 29246): 262.937813572471, (43, 29248): 262.4658706562594, (43, 29282): 260.25151946801583, (43, 29290): 264.3838414855798, (43, 29291): 263.8382969216604, (43, 29292): 264.30416070683873, (43, 29293): 263.4219768357778, (43, 29294): 263.99052232714547, (43, 29298): 263.4057951675297, (43, 29299): 263.24593013900767, (43, 29304): 262.60783548502866, (43, 29317): 260.6009418435903, (43, 29323): 260.45458643367556, (43, 29330): 261.40687200900635, (43, 29331): 261.95006498842844, (43, 29344): 253.8845047533526, (43, 29445): 232.77535412132457, (43, 29724): 142.25905728514846, (43, 29738): 142.41191751638263, (43, 29745): 142.44925665950592, (43, 29748): 144.9779173777583, (43, 29750): 146.2534102246928, (43, 29759): 144.4711391760423, (43, 29772): 145.07192126736015, (43, 29781): 145.01015079908956, (43, 29784): 143.8603178329144, (43, 29790): 145.57092782095563, (43, 29811): 146.310086437619, (43, 29817): 153.76775146682638, (43, 29818): 153.74784490639118, (43, 29929): 140.87299452623776, (43, 30039): 136.1590111039871, (43, 30066): 130.90073471339153, (43, 30116): 131.17031757217416, (43, 30238): 132.71253142967885, (43, 30248): 124.64467830597049, (43, 30260): 124.00446991060234, (43, 30545): 250.0883583983464, (43, 30733): 231.66905601788682, (43, 30756): 225.28979398548995, (43, 30921): 234.97766743435895, (43, 31079): 192.8013653421108, (43, 31149): 189.41984672273455, (43, 31154): 189.60016697417473, (43, 31160): 189.25203993129978, (43, 31163): 189.29057273268245, (43, 31189): 180.8520961090329, (43, 31215): 181.46925814247058, (43, 31259): 181.042032696311, (43, 31262): 180.09811135832058, (43, 31430): 194.02847750429282, (43, 31568): 172.16536013998606, (43, 31751): 188.6538124971023, (44, 109): 77.88810002347485, (44, 872): 236.43336384766974, (44, 873): 237.32776178328123, (44, 877): 236.9866242825585, (44, 879): 237.1187677762869, (44, 884): 236.20762231570689, (44, 889): 236.7708843840968, (44, 891): 235.91312645910898, (44, 892): 237.8133027048935, (44, 894): 237.70265860185404, (44, 896): 236.85022994533495, (44, 903): 237.01384583163969, (44, 909): 235.50946752577624, (44, 910): 235.8729685253018, (44, 912): 235.2801502669284, (44, 913): 234.62496542507597, (44, 916): 234.35558692058763, (44, 926): 236.17342887690367, (44, 927): 235.87432597610828, (44, 948): 235.5897896381412, (44, 961): 236.12880104416033, (44, 962): 236.23405946826756, (44, 963): 236.35116767070744, (44, 967): 237.39429406839707, (44, 974): 236.9014081009422, (44, 998): 237.74370010461254, (44, 1014): 257.3581292258358, (44, 1086): 234.38101759242596, (44, 1087): 234.2832978519275, (44, 1089): 233.44910685736426, (44, 1090): 233.82541266784563, (44, 1092): 235.1163269389131, (44, 1097): 234.12872336942297, (44, 1107): 235.7683685280169, (44, 1387): 100.35146887031662, (44, 1554): 86.33408637018864, (44, 1827): 277.1213248743254, (44, 1828): 277.22099320937537, (44, 1829): 277.35523107221906, (44, 1830): 277.19173718472024, (44, 1831): 277.27591950801525, (44, 1832): 277.181629481782, (44, 1833): 277.19616629780825, (44, 1836): 277.0971205816611, (44, 1841): 277.6654449322923, (44, 1843): 277.42504399248276, (44, 1844): 277.5283813360302, (44, 1845): 277.2389043343539, (44, 1847): 276.3232788089899, (44, 1848): 276.6409863503344, (44, 1849): 278.1262977776842, (44, 1850): 278.2856762561501, (44, 1851): 276.87425525562986, (44, 1852): 276.88899776082917, (44, 1854): 277.0479196679975, (44, 1856): 276.2668010776102, (44, 1857): 276.6146266179078, (44, 1858): 277.9874731759294, (44, 1861): 277.3278081875646, (44, 1866): 276.2391298684702, (44, 1867): 277.6892349585463, (44, 1868): 277.5032075900223, (44, 1870): 277.49086490925794, (44, 1871): 277.652807932528, (44, 1875): 277.0375552451851, (44, 1880): 276.47358298502917, (44, 1882): 276.55541047666446, (44, 1883): 278.3077371029629, (44, 1889): 276.6541062038766, (44, 1893): 277.3864494890632, (44, 1894): 277.1633633071871, (44, 1899): 276.46105934254615, (44, 1900): 276.6300927759688, (44, 1902): 277.7776646395251, (44, 1905): 278.06296538924516, (44, 1907): 276.8663387105986, (44, 1910): 276.98401085263225, (44, 1917): 278.7025243562498, (44, 1920): 276.89558001347535, (44, 1935): 278.1188835937133, (44, 1937): 278.36396101922753, (44, 1946): 275.9787767836466, (44, 1949): 276.2605146870043, (44, 1950): 275.2651038987031, (44, 1951): 275.740978613926, (44, 1952): 276.07228840173303, (44, 1953): 276.2445779096644, (44, 1954): 276.0088095433304, (44, 1958): 276.17291178223695, (44, 1960): 276.6394571381889, (44, 1968): 276.82361535396046, (44, 1969): 278.1915933770335, (44, 1974): 277.83248671757184, (44, 1975): 277.82371581255586, (44, 1979): 277.16283377068095, (44, 1980): 277.0954952789039, (44, 1981): 277.30073498877647, (44, 1985): 277.46627062861137, (44, 1994): 274.8517739533359, (44, 2011): 276.53845155451734, (44, 2019): 278.8588336850584, (44, 2020): 278.55187349317976, (44, 2029): 277.3721450745516, (44, 2030): 278.3393417164923, (44, 2032): 277.1718976771569, (44, 2033): 277.8057676073881, (44, 2034): 277.78771170864525, (44, 2036): 276.58060311218213, (44, 2037): 276.89072673335875, (44, 2038): 277.0259848417072, (44, 2042): 280.58803120904224, (44, 2050): 277.65581194819737, (44, 2051): 277.5966612333202, (44, 2053): 277.6946172396235, (44, 2054): 278.00952468289245, (44, 2066): 277.3673212812684, (44, 2067): 277.37333412878814, (44, 2071): 274.26095990725497, (44, 2072): 274.85752470913565, (44, 2073): 273.2533791240589, (44, 2074): 273.168758953058, (44, 2080): 272.15862714771146, (44, 2082): 275.1776071521754, (44, 2083): 275.48652135206254, (44, 2089): 274.8421880300131, (44, 2090): 275.1315175542338, (44, 2092): 274.7458192343882, (44, 2098): 272.5495879482354, (44, 2099): 272.8903198912426, (44, 2101): 272.4816937404786, (44, 2102): 274.1037352879183, (44, 2103): 273.59145940695174, (44, 2104): 273.3086654298016, (44, 2106): 275.6906138557403, (44, 2112): 272.6921914579774, (44, 2113): 274.33122406536796, (44, 2114): 274.71265705024683, (44, 2117): 275.92906795752475, (44, 2123): 273.75347028486567, (44, 2124): 274.087856777143, (44, 2134): 273.1255607660525, (44, 2138): 274.11326987264, (44, 2141): 273.2443740447057, (44, 2148): 273.69557640654443, (44, 2150): 272.4287560297627, (44, 2151): 272.77799450535, (44, 2152): 272.2413545224641, (44, 2153): 273.8122027135925, (44, 2154): 272.4291432917516, (44, 2155): 272.2630126705803, (44, 2156): 272.00996984945164, (44, 2157): 272.3369168058177, (44, 2160): 274.56301599964576, (44, 2161): 272.18000209145225, (44, 2162): 273.85550317959206, (44, 2163): 273.3870789178455, (44, 2164): 273.3532004629292, (44, 2168): 272.5448791574056, (44, 2172): 272.8396197810917, (44, 2174): 272.7329171424517, (44, 2178): 273.10876750507794, (44, 2179): 272.89098773520425, (44, 2183): 274.0862381623892, (44, 2185): 274.1050706920689, (44, 2186): 273.83933631491317, (44, 2190): 274.6325798844807, (44, 2192): 274.1533312883782, (44, 2193): 274.1812262055441, (44, 2194): 273.69166808638676, (44, 2195): 273.61610999379997, (44, 2197): 274.255932844359, (44, 2205): 273.564101004906, (44, 2207): 272.6652554044635, (44, 2208): 273.1670287331841, (44, 2212): 274.3344954266421, (44, 2214): 264.3636373946174, (44, 2225): 265.522283940745, (44, 2231): 263.3191114084697, (44, 2278): 270.3571350245594, (44, 2284): 271.3541102621224, (44, 2285): 271.2088495431084, (44, 2291): 269.178079819693, (44, 2292): 269.43250724346865, (44, 2307): 270.69823064895826, (44, 2313): 268.9297828110994, (44, 2317): 268.7025730255997, (44, 2319): 269.7756412494402, (44, 2321): 270.2322776316031, (44, 2323): 270.1816229392003, (44, 2326): 271.96277586337845, (44, 2327): 271.5265816789595, (44, 2329): 271.2277943874963, (44, 2330): 270.8849823183251, (44, 2332): 271.5987166189797, (44, 2344): 270.5012365293743, (44, 2346): 270.47367805489995, (44, 2361): 270.36318397897094, (44, 2368): 275.4177632904103, (44, 2374): 275.89233436549864, (44, 2375): 276.0565259805457, (44, 2377): 274.38579695607973, (44, 2378): 276.35582248475555, (44, 2379): 276.39072107959606, (44, 2380): 276.5614333074423, (44, 2383): 274.8372635664887, (44, 2385): 275.0985292815919, (44, 2395): 275.1336882752151, (44, 2397): 276.1881423817423, (44, 2398): 273.8527286744279, (44, 2399): 274.4589097101704, (44, 2400): 274.3238779762136, (44, 2402): 275.2602587607821, (44, 2403): 275.634190430596, (44, 2404): 275.7336329872646, (44, 2405): 274.82967570844846, (44, 2407): 275.57057621508557, (44, 2408): 276.00618916075615, (44, 2409): 275.10506439475654, (44, 2411): 275.6185970284463, (44, 2412): 275.5253260780188, (44, 2413): 275.830328191413, (44, 2414): 275.32980733737503, (44, 2422): 275.50017558328096, (44, 2424): 275.6337222081105, (44, 2426): 275.7173744760717, (44, 2433): 275.0151474496448, (44, 2436): 274.8211091900535, (44, 2437): 272.6395742649754, (44, 2440): 273.1227008047868, (44, 2445): 282.70564074670756, (44, 2447): 281.52672869052884, (44, 2454): 282.6450556779195, (44, 2455): 282.71485582681197, (44, 2460): 279.23199274060414, (44, 2461): 279.6601956630999, (44, 2471): 286.54582405144, (44, 2492): 278.8326846689251, (44, 2511): 275.42161162929096, (44, 2523): 277.164853602045, (44, 2525): 276.61811787066466, (44, 2535): 277.73739560533676, (44, 2537): 276.96234934994675, (44, 2538): 277.507909190729, (44, 2539): 277.2296120376623, (44, 2540): 278.08764492897774, (44, 2542): 278.6301116543396, (44, 2559): 289.68711934171256, (44, 2575): 288.63322993682334, (44, 2599): 272.2090657055133, (44, 2600): 275.88435647831386, (44, 2607): 273.800990898906, (44, 2627): 277.3599418821281, (44, 2647): 279.35421423122597, (44, 2674): 278.3736672310971, (44, 2681): 278.0591616165727, (44, 2683): 279.06670262368675, (44, 2686): 277.94147254296115, (44, 2689): 291.16449355334083, (44, 2690): 291.2213339840883, (44, 2713): 293.5629407534488, (44, 2714): 293.7565753390561, (44, 2715): 294.0842550588433, (44, 2739): 293.8022476119191, (44, 2740): 291.81672745277086, (44, 2741): 291.98546336002374, (44, 2749): 293.31896028525097, (44, 2750): 293.431758455615, (44, 2752): 293.6701180806236, (44, 2755): 293.92268469406673, (44, 2758): 293.83836198050136, (44, 2759): 293.8441392014347, (44, 2769): 293.4753114797075, (44, 2771): 292.3245395499635, (44, 2779): 292.3519060634709, (44, 2784): 288.6314354655302, (44, 2800): 289.21793586578644, (44, 2802): 291.14274567754023, (44, 2803): 291.0273135120943, (44, 2804): 290.8120393154567, (44, 2805): 291.3909802718402, (44, 2807): 291.37981599259007, (44, 2809): 291.23714604857577, (44, 2812): 289.1580577208767, (44, 2814): 291.065180398033, (44, 2817): 291.05469353411087, (44, 2819): 291.4452754435661, (44, 2823): 289.28227510167443, (44, 2832): 291.78494533983513, (44, 2836): 290.3106859437185, (44, 2839): 291.3845113230105, (44, 2841): 291.16946417784175, (44, 2843): 291.07471639357175, (44, 2846): 290.56417505165587, (44, 2849): 291.99930048774934, (44, 2852): 291.6704419317516, (44, 2853): 292.15009676171866, (44, 2876): 292.2558661291338, (44, 2877): 293.4321608863474, (44, 2885): 293.701468721523, (44, 2918): 291.6711118417684, (44, 2921): 292.16908532179775, (44, 2925): 289.85974949752983, (44, 2926): 289.1040298912833, (44, 2930): 290.7625302286003, (44, 2931): 290.0555049095241, (44, 2938): 291.66195935369393, (44, 2940): 293.21251931135515, (44, 2947): 291.49415545581786, (44, 2949): 290.78262498170983, (44, 2950): 290.9961341700669, (44, 2952): 290.74457827604044, (44, 2958): 290.7018798646584, (44, 2959): 290.96148381385063, (44, 2960): 291.51495531937627, (44, 2961): 291.2394719114273, (44, 2963): 290.48036003450835, (44, 2968): 290.63114300235395, (44, 2976): 290.4227560085291, (44, 2981): 285.5355711538133, (44, 2982): 285.37998772046393, (44, 2984): 285.1272286632991, (44, 3003): 284.6707360404136, (44, 3046): 281.6149692547599, (44, 3050): 284.0790516277067, (44, 3051): 284.28237221733934, (44, 3053): 283.72630961081353, (44, 3069): 286.7645773384576, (44, 3071): 283.6334983489175, (44, 3080): 293.67787307529244, (44, 3199): 283.75279099271654, (44, 3200): 283.16147492381333, (44, 3205): 286.7452861209344, (44, 3209): 283.4625650479049, (44, 3215): 283.20646251897216, (44, 3217): 282.4900313719846, (44, 3249): 283.28119793835276, (44, 3263): 288.69475063639123, (44, 3289): 285.0154178227344, (44, 3301): 285.16421146633957, (44, 3302): 284.9146174841006, (44, 3307): 284.5954207307702, (44, 3310): 285.47257874755616, (44, 3391): 285.6840770725336, (44, 3509): 170.31771880863195, (44, 3510): 169.80823801208362, (44, 3511): 170.1626767875853, (44, 3512): 169.8608252616819, (44, 3514): 169.9799769690641, (44, 3519): 171.44029095040972, (44, 3536): 171.24312829558136, (44, 3545): 172.0579109032503, (44, 3548): 171.2965755634695, (44, 3572): 171.5141316768453, (44, 3581): 170.84708873623376, (44, 3583): 170.56179553002755, (44, 3601): 172.3749427908281, (44, 3656): 171.4931948314659, (44, 3669): 170.3833539966484, (44, 3670): 170.83590082814882, (44, 3695): 168.2704431712531, (44, 3696): 168.6336025317621, (44, 3782): 171.75463431074547, (44, 3792): 171.15210080043994, (44, 3989): 48.644847145247326, (44, 4008): 51.477526873812884, (44, 4031): 51.595188522936546, (44, 4045): 50.3011458147531, (44, 4144): 50.22006409567889, (44, 4145): 47.20088089204094, (44, 4164): 49.078463409006545, (44, 4168): 48.10901286108331, (44, 4173): 47.890043173923424, (44, 4181): 46.180285577406586, (44, 4228): 44.752271362381954, (44, 4248): 43.81788464360499, (44, 4254): 29.905299617992867, (44, 4260): 29.73175422686297, (44, 4262): 30.7413459492509, (44, 4273): 30.418195612349702, (44, 4319): 24.798172724838388, (44, 4326): 24.490750807128432, (44, 4328): 24.43746363413567, (44, 4334): 25.184043944174427, (44, 4335): 25.129677048358307, (44, 4372): 93.2418262517127, (44, 4413): 100.60446411545357, (44, 4434): 92.465247775351, (44, 4447): 91.44487888681167, (44, 4452): 92.8065233700918, (44, 4463): 95.02098377957644, (44, 4465): 94.57524420290365, (44, 4619): 106.47136924739884, (44, 4645): 106.3925210737456, (44, 4657): 106.92830593232308, (44, 4666): 107.22789706679328, (44, 4676): 107.72244584379068, (44, 4678): 107.52679841253595, (44, 4689): 107.95872393375684, (44, 4704): 110.67985265152913, (44, 4726): 131.28010812870505, (44, 4727): 130.95439662099477, (44, 4730): 130.282823216745, (44, 4731): 130.74060825396137, (44, 4734): 129.58151968440654, (44, 4735): 129.50070595755707, (44, 4736): 129.85456736248173, (44, 4737): 129.57662292267176, (44, 4738): 129.80989607931303, (44, 4756): 130.2569947241316, (44, 4760): 127.50670805725848, (44, 4761): 127.24176218282633, (44, 4762): 127.33498373038725, (44, 4765): 127.80115612499392, (44, 4773): 131.70088698769086, (44, 4774): 131.77244608780018, (44, 4790): 131.43012348581166, (44, 4795): 131.05485956884016, (44, 4799): 132.1048869121551, (44, 4801): 133.28097933313603, (44, 4804): 130.71227102583734, (44, 4805): 130.40906705345745, (44, 4806): 132.1829737195876, (44, 4815): 132.1904553813762, (44, 4816): 132.83947010518992, (44, 4817): 133.41667415658034, (44, 4826): 132.80419998261394, (44, 4830): 132.52110042818794, (44, 4839): 128.47497403577586, (44, 4840): 128.945438041165, (44, 4841): 128.4069333256163, (44, 4846): 128.11066642641765, (44, 4848): 128.40036557617705, (44, 4850): 128.75715792119192, (44, 4871): 123.3266664244528, (44, 4883): 126.61096729557434, (44, 4900): 124.40755587923005, (44, 4901): 124.29590834825846, (44, 4917): 113.90535455202834, (44, 4931): 112.20947689697651, (44, 4944): 113.81494274090817, (44, 4956): 112.8036705759285, (44, 4958): 113.31884264448809, (44, 4959): 113.386772324012, (44, 4961): 112.91549799116815, (44, 4966): 112.71968554587136, (44, 5207): 110.93605897936924, (44, 5272): 64.77823831325962, (44, 5283): 65.33418449347653, (44, 5287): 67.78586475163661, (44, 5289): 68.09598183518236, (44, 5293): 63.35471497461216, (44, 5295): 64.71945584976767, (44, 5296): 65.65580351590354, (44, 5298): 66.16639696157286, (44, 5303): 67.38870068702452, (44, 5305): 66.3460396511062, (44, 5306): 67.32651583244305, (44, 5307): 66.18375290567153, (44, 5308): 66.87255249158967, (44, 5313): 65.65634219504548, (44, 5314): 65.59969549580875, (44, 5317): 67.49369355527254, (44, 5319): 67.13357208959673, (44, 5324): 66.13129554769162, (44, 5326): 65.43161337733869, (44, 5348): 68.0347329982915, (44, 5351): 69.70257226349437, (44, 5399): 69.75474464343012, (44, 5413): 72.38827533423554, (44, 5422): 69.09173735155278, (44, 5445): 68.38710628820647, (44, 5448): 67.94921479849245, (44, 5456): 68.84797573197534, (44, 5467): 69.51779337046555, (44, 5624): 62.01655266057043, (44, 5671): 65.11793005525574, (44, 5672): 64.14600149204554, (44, 5797): 76.64410891884475, (44, 5871): 85.4677158543903, (44, 5976): 80.02172724496002, (44, 6118): 231.33525303313877, (44, 6248): 242.21732178151748, (44, 6345): 55.93124155069937, (44, 6352): 58.45427251259518, (44, 6354): 55.27432049097668, (44, 6359): 54.8506693665988, (44, 6376): 58.2626998441985, (44, 6378): 55.58088764680003, (44, 6381): 55.11048415453897, (44, 6383): 56.43546176648591, (44, 6396): 55.74465362860404, (44, 6399): 55.99392852152131, (44, 6408): 58.28403254120075, (44, 6409): 56.91711772979195, (44, 6419): 60.6988261031015, (44, 6422): 57.80373800053344, (44, 6423): 57.99613177941932, (44, 6424): 55.3229009656931, (44, 6439): 55.750726563952725, (44, 6464): 56.39312387737441, (44, 6465): 56.69538969260909, (44, 6469): 56.507306670208294, (44, 6470): 56.69168959245686, (44, 6472): 54.026357412982485, (44, 6480): 54.2513613472127, (44, 6486): 52.56056473915346, (44, 6497): 53.10236527989733, (44, 6503): 55.97770080452928, (44, 6508): 55.925538998310905, (44, 6509): 55.38958606705365, (44, 6521): 53.83233708163012, (44, 6544): 53.875402448131986, (44, 6552): 57.09505066714639, (44, 6553): 57.46511138105366, (44, 6554): 57.84350722134461, (44, 6578): 56.49764504260528, (44, 6582): 56.63875825204211, (44, 6601): 56.29604819177433, (44, 6609): 53.45653649648331, (44, 6610): 53.31082831633049, (44, 6611): 53.33974029413226, (44, 6614): 53.60309600895516, (44, 6615): 53.49388653708111, (44, 6616): 52.96466967202282, (44, 6617): 53.18290894978727, (44, 6618): 52.50183705934701, (44, 6619): 53.85429533773689, (44, 6620): 52.89817907064163, (44, 6621): 53.20778872728765, (44, 6622): 53.172087267474204, (44, 6623): 53.561688027304136, (44, 6624): 53.77981381008705, (44, 6625): 53.874727117345174, (44, 6626): 53.903469700866154, (44, 6627): 53.746643858507056, (44, 6628): 52.909725579050516, (44, 6629): 53.61646573485169, (44, 6630): 54.261417634112995, (44, 6632): 53.682089413001364, (44, 6634): 54.56385272051628, (44, 6635): 53.35385859186107, (44, 6636): 52.9258912101085, (44, 6637): 54.05132551841974, (44, 6638): 54.15544086686216, (44, 6639): 53.67001287472636, (44, 6640): 54.13623717500235, (44, 6641): 53.17391615881344, (44, 6642): 54.10357635255149, (44, 6643): 53.99253750652529, (44, 6645): 53.77763231585339, (44, 6646): 52.66156079827491, (44, 6647): 54.03102653130984, (44, 6653): 53.53005559989784, (44, 6655): 53.690288969850336, (44, 6658): 54.56093025284109, (44, 6662): 54.07652542614224, (44, 6819): 71.85146567628976, (44, 6996): 65.74863607858484, (44, 7059): 61.54155197486068, (44, 7187): 71.63518683140373, (44, 7304): 78.3010612295258, (44, 7528): 66.93508155332664, (44, 7720): 41.562621747116474, (44, 7793): 42.649921278153684, (44, 7807): 42.110953334639454, (44, 7808): 42.92810691022272, (44, 7831): 50.784712466500686, (44, 7850): 46.936154669171835, (44, 7852): 47.95305197895566, (44, 8012): 42.205168549931436, (44, 8125): 45.058270363642585, (44, 8208): 34.29498959706417, (44, 8392): 47.78839628507964, (44, 8651): 92.31600864481379, (44, 9088): 74.36691703016855, (44, 9443): 103.73812182016434, (44, 9444): 103.2211680085182, (44, 9828): 123.90758912633986, (44, 9868): 122.54844315565836, (44, 10180): 45.44052710947472, (44, 10256): 38.76528950219452, (44, 10276): 40.15860902113891, (44, 10378): 34.988395637607134, (44, 10676): 54.98940191258641, (44, 10714): 61.74878087618777, (44, 10730): 55.841643951718794, (44, 10862): 120.06748580681324, (44, 10881): 120.00451277649218, (44, 10883): 120.27339190727315, (44, 10885): 120.01768896480675, (44, 10891): 120.69848674761498, (44, 10909): 120.07798355733138, (44, 10911): 119.42669808140857, (44, 10913): 119.64844549562646, (44, 10915): 119.3177690082549, (44, 10919): 119.03058972587296, (44, 11037): 127.62374946350775, (44, 11039): 125.3468908983523, (44, 11516): 83.20570362045876, (44, 11856): 25.42172527836267, (44, 11857): 25.676595940780103, (44, 11861): 25.567960515364778, (44, 11881): 24.42074142530129, (44, 11902): 22.74748806596392, (44, 11911): 21.88615848199361, (44, 11914): 22.358287885071878, (44, 11922): 23.79871648533039, (44, 11924): 24.06079899785635, (44, 11926): 23.540350927654234, (44, 11950): 23.97263366518824, (44, 11963): 25.68986482859082, (44, 11983): 23.80287185733572, (44, 11985): 26.594341085547274, (44, 12009): 25.631761281742428, (44, 12010): 24.548093704542826, (44, 12018): 24.667478462084812, (44, 12020): 25.08890163738923, (44, 12021): 25.225290671075907, (44, 12024): 26.40035629810967, (44, 12025): 26.125755854577747, (44, 12027): 25.81724560937554, (44, 12031): 24.346938898145286, (44, 12032): 24.853618866698586, (44, 12035): 25.42228735115353, (44, 12041): 27.1535051138845, (44, 12045): 12.5, (44, 12145): 17.051052588682175, (44, 12275): 50.57967152742393, (44, 12294): 48.38128318229462, (44, 12358): 58.00420887964567, (44, 12463): 62.20070465836739, (44, 12465): 62.13845175256343, (44, 12482): 63.078761440559724, (44, 12503): 63.007347502967825, (44, 12506): 63.41197497884304, (44, 12549): 61.87362835519613, (44, 12559): 61.689879597371814, (44, 12569): 62.257048066840014, (44, 12572): 62.54916025995057, (44, 12574): 61.865482129670745, (44, 12576): 62.15454763405679, (44, 12591): 61.73398764932529, (44, 12608): 64.0277815194893, (44, 12696): 59.76323667577066, (44, 12710): 61.75984024491812, (44, 12728): 61.006399881304176, (44, 12766): 28.086628681756036, (44, 12771): 27.042543463900433, (44, 12790): 27.472129894684933, (44, 12795): 28.823920898069435, (44, 12797): 30.50670824806556, (44, 12798): 29.938106007346686, (44, 12811): 27.419684989533092, (44, 12830): 28.730962472971346, (44, 12848): 27.30829177134346, (44, 12850): 26.517010664502607, (44, 12852): 28.550256873658757, (44, 12854): 28.941703508761147, (44, 12859): 26.66089539068011, (44, 12861): 29.281235966525653, (44, 12865): 27.422321278513472, (44, 12866): 27.301971542157556, (44, 12867): 26.85404730924484, (44, 12874): 27.109358169542315, (44, 12875): 26.699797071464832, (44, 12881): 28.197085743185532, (44, 12883): 27.703254872045612, (44, 12885): 26.536670216952878, (44, 12888): 27.712579051108907, (44, 12889): 27.62000965093516, (44, 12892): 27.153071630962277, (44, 12893): 27.906438082754708, (44, 12896): 27.470090832038867, (44, 12906): 28.064941743879032, (44, 13018): 37.165039084605155, (44, 13071): 38.52351885897949, (44, 13131): 36.45846748067653, (44, 13146): 32.81199856138986, (44, 13159): 42.646124949570414, (44, 13193): 36.68128229597941, (44, 13198): 40.365260672049, (44, 13292): 33.77012254984191, (44, 13296): 30.447354609764908, (44, 13406): 46.10687538051556, (44, 13407): 46.4817717681357, (44, 13417): 48.546127023836135, (44, 13418): 48.279899301912266, (44, 13438): 44.64099313929712, (44, 13442): 43.61088257931516, (44, 13443): 44.12523997508989, (44, 13764): 95.63026203063922, (44, 13766): 94.99554167231832, (44, 13771): 96.17689627028281, (44, 13783): 95.2486987542515, (44, 13784): 94.062361390428, (44, 13792): 98.25428026659571, (44, 13824): 95.79483318051444, (44, 14017): 89.02566341690395, (44, 14870): 106.71974224694297, (44, 14997): 74.93697273239674, (44, 15000): 75.00168168602376, (44, 15003): 74.71000414405594, (44, 15006): 73.19416594510983, (44, 15007): 72.77309883138062, (44, 15056): 73.20929053357673, (44, 15063): 73.6719371877566, (44, 15069): 73.97260712178132, (44, 15076): 72.79071146400881, (44, 15086): 74.00029025779371, (44, 15087): 74.63061871041205, (44, 15111): 75.82022380008944, (44, 15116): 75.1471511854555, (44, 15722): 86.6640137739862, (44, 15998): 97.75498393321594, (44, 16073): 192.02896593180932, (44, 16939): 248.44812447046874, (44, 16940): 247.79122701886172, (44, 16951): 248.50642953995273, (44, 16963): 248.57762813273735, (44, 16965): 249.39149312215937, (44, 16969): 249.17697066464117, (44, 16970): 248.8785867392426, (44, 16971): 248.14646116355405, (44, 16973): 248.08571490298525, (44, 16974): 249.70749504993407, (44, 16976): 248.9427090997234, (44, 16978): 248.41189606511782, (44, 16980): 249.22320003128502, (44, 16982): 249.689684301815, (44, 17045): 271.16244108122567, (44, 17048): 272.10022822037956, (44, 17304): 39.73319501130521, (44, 17305): 39.32389542566562, (44, 17330): 39.744912769308954, (44, 17334): 38.82096630238296, (44, 17343): 40.43730823305901, (44, 17345): 38.84030682149419, (44, 17347): 39.7321558023515, (44, 17351): 37.590767934656, (44, 17372): 38.73538703323697, (44, 17373): 40.37353525970385, (44, 17377): 40.494533143447704, (44, 17382): 39.438672466690036, (44, 17383): 39.61441884534802, (44, 17389): 38.9965079099842, (44, 17400): 40.06093631653717, (44, 17401): 40.03187506708929, (44, 17402): 40.12866649736393, (44, 17403): 40.238635794497156, (44, 17440): 39.00406223928521, (44, 17455): 40.30715484715402, (44, 17491): 40.488026878581714, (44, 17507): 38.22236016716163, (44, 17509): 38.81810214362628, (44, 17590): 37.25934859369084, (44, 17615): 34.45003604680924, (44, 17642): 34.92070625781812, (44, 17643): 34.802966473123455, (44, 17668): 34.47962564562522, (44, 17721): 33.764565621986435, (44, 17754): 39.20024248497599, (44, 17769): 38.50862033069023, (44, 17776): 36.06582275896099, (44, 17804): 39.46641194947899, (44, 17809): 40.04706581803682, (44, 17824): 39.7441528797252, (44, 17837): 37.82595240276703, (44, 17838): 37.88324514215295, (44, 17862): 37.448862292348785, (44, 17866): 38.69414914796037, (44, 17872): 37.027556618427525, (44, 17873): 36.07555863911181, (44, 17881): 37.53678001102615, (44, 17947): 194.7877462751121, (44, 17951): 193.52725155646965, (44, 17953): 193.2873453490447, (44, 17954): 193.37618536545634, (44, 17959): 194.5271963933734, (44, 17963): 194.0817307172156, (44, 18000): 187.6741799045564, (44, 18001): 187.92718372013348, (44, 18111): 206.01275946786149, (44, 18148): 173.8428922407398, (44, 18166): 186.34447819624887, (44, 18189): 197.89716674225647, (44, 18239): 40.64961329037606, (44, 18240): 40.64532888021263, (44, 18245): 40.705895734336536, (44, 18247): 40.58044945834898, (44, 18251): 40.70733747537963, (44, 18256): 40.84912100090878, (44, 18258): 40.703915582828415, (44, 18259): 40.73278214171329, (44, 18260): 40.79349240927443, (44, 18262): 40.905807800947315, (44, 18263): 40.89010595031142, (44, 18264): 40.95002148238901, (44, 18266): 40.95421404131995, (44, 18267): 41.01292961865669, (44, 18268): 41.04404136426841, (44, 18269): 41.162443997780024, (44, 18275): 41.10653350155899, (44, 18285): 40.927942296752846, (44, 18308): 39.74424868933836, (44, 18313): 39.351486042986004, (44, 18314): 39.526630989660525, (44, 18315): 41.140242040258954, (44, 18316): 41.13803174520095, (44, 18317): 41.193751441589036, (44, 18320): 41.23496329071755, (44, 18321): 41.2689301030017, (44, 18322): 41.35521342905688, (44, 18324): 41.41416636161269, (44, 18325): 41.67116500773742, (44, 18326): 41.57505586353131, (44, 18327): 41.252277161132696, (44, 18329): 41.77833449147169, (44, 18330): 41.67511568997521, (44, 18331): 41.4983838056482, (44, 18332): 41.32108637306978, (44, 18333): 41.64031531292974, (44, 18336): 41.48416471643633, (44, 18337): 41.566905323247155, (44, 18403): 41.48721109165737, (44, 18432): 38.55673748563853, (44, 18451): 40.48817327681279, (44, 18466): 42.58142611320323, (44, 18481): 41.19088621329541, (44, 18483): 41.19471241212925, (44, 18484): 41.05068504930611, (44, 18485): 40.61705599313658, (44, 18486): 40.98741544291918, (44, 18487): 40.6604020141844, (44, 18489): 40.9544795118928, (44, 18490): 41.27493093659388, (44, 18491): 41.42864102411534, (44, 18492): 40.33316821771911, (44, 18493): 40.93166522120874, (44, 18494): 40.89404931380853, (44, 18495): 41.16016996923254, (44, 18496): 41.00046537981623, (44, 18497): 40.58511217547836, (44, 18498): 40.66342505256272, (44, 18499): 40.903575907347, (44, 18501): 40.72717359961715, (44, 18502): 40.57389109875232, (44, 18503): 40.45748891705996, (44, 18504): 41.06669409905317, (44, 18506): 40.748386949338624, (44, 18507): 40.60311343317693, (44, 18508): 40.86834849040885, (44, 18509): 40.87003837717267, (44, 18510): 40.46016308276119, (44, 18511): 40.976842761393556, (44, 18512): 40.79706572889566, (44, 18515): 41.07823496015078, (44, 18516): 41.08620193874921, (44, 18517): 40.893092060654, (44, 18518): 41.213310698179626, (44, 18519): 41.10143744399624, (44, 18520): 40.82516844033023, (44, 18522): 41.76377598737833, (44, 18523): 41.79271145590266, (44, 18532): 42.00082796605762, (44, 18535): 41.56416696174131, (44, 18537): 41.32118617167448, (44, 18539): 41.369646072338675, (44, 18540): 41.39561541517225, (44, 18541): 41.513577036916296, (44, 18542): 41.58892912977252, (44, 18543): 41.21337435557165, (44, 18546): 41.38562012132531, (44, 18555): 41.76744477883328, (44, 18556): 41.83517675029763, (44, 18565): 41.96736998067629, (44, 18567): 42.07289865608589, (44, 18568): 41.86700972736796, (44, 18577): 43.36335111265776, (44, 18583): 43.11975405139575, (44, 18605): 43.4469265140884, (44, 18608): 42.19524712904881, (44, 18616): 44.83919462617444, (44, 18618): 46.02280148964544, (44, 18625): 45.64309352331992, (44, 18645): 44.61928750638129, (44, 18646): 44.87446559516711, (44, 18653): 43.85042735568186, (44, 18654): 44.80487704396761, (44, 18655): 44.172238069099805, (44, 18666): 48.07665910978482, (44, 18837): 47.13959139424896, (44, 18974): 40.94107750774868, (44, 18999): 42.22858052889762, (44, 19000): 42.574041809255036, (44, 19174): 31.561340325080614, (44, 19342): 38.76076958871937, (44, 19455): 30.078472195084363, (44, 19555): 21.58661237375261, (44, 19564): 25.51697964945408, (44, 19573): 24.48522893449979, (44, 19586): 23.7944070300128, (44, 19605): 23.322651068990638, (44, 19611): 23.888500025962127, (44, 19614): 22.66482435681606, (44, 19641): 28.848743090298115, (44, 19702): 29.69538848488998, (44, 19713): 29.00006511882791, (44, 19731): 15.266303292541755, (44, 19819): 29.174041573947488, (44, 19893): 38.80218139142708, (44, 19899): 43.239572022154924, (44, 19929): 39.0732718638498, (44, 19951): 45.2905197922327, (44, 19962): 41.181682078039536, (44, 19970): 39.141348780666526, (44, 19971): 39.933499761866756, (44, 19972): 39.99444943991081, (44, 19975): 39.2247056595666, (44, 19978): 43.43040818337841, (44, 19987): 43.066014446137636, (44, 19989): 41.195061690695105, (44, 20039): 43.18306665670748, (44, 20043): 43.32944873656758, (44, 20047): 42.12762104779428, (44, 20052): 40.56576810932629, (44, 20054): 41.045851593304114, (44, 20085): 46.93374029131329, (44, 20104): 47.47696993909409, (44, 20132): 44.85289828942372, (44, 20203): 45.688832598290425, (44, 20280): 47.4622389246068, (44, 20285): 48.29939993127438, (44, 20290): 47.231520325286155, (44, 20297): 46.63639959655219, (44, 20309): 49.012582612082646, (44, 20453): 54.21016847670786, (44, 20485): 43.399549183050254, (44, 20520): 42.04790230210537, (44, 20526): 44.17110082745443, (44, 20698): 122.99473960589646, (44, 20868): 145.9737638414949, (44, 21042): 22.11632033998961, (44, 21057): 17.244860131720745, (44, 21066): 19.897956121052996, (44, 21075): 20.447708580956448, (44, 21093): 22.12356696957602, (44, 21098): 19.448093299072802, (44, 21127): 21.90321816720721, (44, 21130): 21.185780841003194, (44, 21144): 20.961890120031605, (44, 21146): 22.218500253470673, (44, 21147): 20.95156311260288, (44, 21148): 20.216850970499898, (44, 21153): 21.622718561535656, (44, 21293): 14.657792891985817, (44, 21426): 16.683029379037894, (44, 21442): 14.652795620907467, (44, 21451): 14.529427742151347, (44, 21466): 15.00568441419307, (44, 21469): 14.305767013569877, (44, 21471): 15.379038746276747, (44, 21473): 14.706551558317043, (44, 21475): 15.209678191657682, (44, 21482): 14.190811089991376, (44, 21484): 14.161948891737248, (44, 21488): 14.653277301229949, (44, 21494): 14.817590172244104, (44, 21498): 14.38321450008958, (44, 21500): 14.786883734999051, (44, 21514): 12.5, (44, 21537): 14.218157030971355, (44, 21662): 12.5, (44, 21691): 13.938060214555565, (44, 21757): 20.563669122029957, (44, 21777): 32.72703453466709, (44, 21778): 33.43182463771854, (44, 21779): 33.280975521596126, (44, 21790): 31.679055394077146, (44, 21802): 32.19154946838872, (44, 21824): 31.733943887504743, (44, 21874): 33.41693973126951, (44, 21879): 34.32906794078673, (44, 21983): 29.023675054064505, (44, 22002): 23.215458388097524, (44, 22132): 25.54988866138489, (44, 22261): 132.98059567655108, (44, 22298): 131.72524005933735, (44, 22339): 141.22409476014414, (44, 22508): 118.21328657537664, (44, 22841): 281.41623639324666, (44, 22842): 281.4479304187142, (44, 22874): 279.7292345460695, (44, 22941): 279.8198673428216, (44, 22956): 280.9523966372475, (44, 22960): 281.2120499511554, (44, 22968): 282.6802359952074, (44, 22970): 282.9314857935447, (44, 22974): 283.7060377975837, (44, 22980): 285.04003393895624, (44, 23025): 285.22011331655665, (44, 23028): 284.9854864443257, (44, 23081): 287.5979773161345, (44, 23104): 285.67403102271464, (44, 23147): 273.0654667932268, (44, 23298): 12.5, (44, 23376): 12.5, (44, 23381): 12.5, (44, 23529): 12.5, (44, 23556): 12.5, (44, 23718): 12.5, (44, 24001): 14.634486986499262, (44, 24094): 18.203162880850517, (44, 24129): 20.301607644889145, (44, 24174): 16.34171659710215, (44, 24235): 21.12540080016937, (44, 24259): 22.809006420035445, (44, 24260): 22.692736906469303, (44, 24261): 22.22020676997322, (44, 24305): 25.112725325059873, (44, 24306): 25.543570133546517, (44, 24307): 24.919297795689545, (44, 24308): 21.01992324254371, (44, 24498): 30.485820345537654, (44, 24499): 30.523511878003724, (44, 24500): 30.13857874294795, (44, 24668): 28.46164634923967, (44, 24711): 33.036109611527614, (44, 24756): 34.509629360888674, (44, 24788): 35.07967921623123, (44, 24809): 32.864893214366404, (44, 24813): 33.525085885135915, (44, 24821): 33.29846065180595, (44, 24825): 33.49648537089139, (44, 24832): 32.690909242375795, (44, 24833): 33.038762006540836, (44, 24835): 33.3962315715897, (44, 24837): 33.93057361223425, (44, 24840): 32.65080113750323, (44, 24841): 33.161642486669095, (44, 24844): 32.68580190522328, (44, 24845): 32.933727084059285, (44, 24846): 33.00232154540461, (44, 24849): 33.200153945960516, (44, 24850): 33.65008753539343, (44, 24863): 28.68646209285902, (44, 24866): 29.295701078425704, (44, 24885): 30.09410736018846, (44, 24886): 30.193293298030664, (44, 24889): 31.426445836016516, (44, 24903): 31.931027149736888, (44, 24909): 29.55764768606787, (44, 24999): 59.07281658654502, (44, 25019): 58.55669152051304, (44, 25028): 58.607233954383, (44, 25137): 57.66439629014247, (44, 25145): 57.64872699611665, (44, 25208): 66.74136194193075, (44, 25233): 66.85531562256585, (44, 25371): 51.99684897966036, (44, 25377): 50.27374593132738, (44, 25828): 61.563030009266114, (44, 25851): 62.887755493977004, (44, 25874): 59.74276754870921, (44, 25898): 61.02316653595627, (44, 25946): 61.77903844062161, (44, 26047): 61.11254919199005, (44, 26066): 39.596392692746576, (44, 26197): 50.760355612186885, (44, 26212): 84.21432844213504, (44, 26253): 86.51829835429264, (44, 26254): 85.45291835415888, (44, 26257): 85.24909976819534, (44, 26258): 86.22870297953835, (44, 26260): 85.67942470712165, (44, 26266): 85.20259397690948, (44, 26267): 84.7554221187022, (44, 26271): 84.89982624910843, (44, 26304): 76.19880010108376, (44, 26305): 75.8259017165851, (44, 26363): 66.35333881657726, (44, 26441): 138.71845584351118, (44, 26442): 138.46519706681607, (44, 26450): 137.2774916745149, (44, 26459): 137.22528581300895, (44, 26462): 137.41032653038, (44, 26467): 140.90056947213606, (44, 26471): 139.9009223608697, (44, 26472): 139.79120790935627, (44, 26473): 139.7452447679692, (44, 26476): 139.13079114969327, (44, 26485): 137.79713657772564, (44, 26493): 137.8130939332019, (44, 26524): 137.9535915936195, (44, 26525): 137.8045284630042, (44, 26556): 139.43083704496655, (44, 26560): 139.35106912963838, (44, 26561): 138.60541220400458, (44, 26564): 139.0994061404875, (44, 26569): 138.40963271720736, (44, 26570): 138.09571161718634, (44, 26573): 138.2700932192389, (44, 26581): 138.22867427421713, (44, 26583): 137.97658511760798, (44, 26593): 138.22030801913314, (44, 26837): 141.12297005755497, (44, 26844): 141.92683419635412, (44, 26863): 140.14555849147303, (44, 26893): 142.44584940923207, (44, 26902): 143.53587674547146, (44, 26905): 142.4597007872908, (44, 26912): 143.301825354453, (44, 26921): 141.24923035612258, (44, 26922): 139.0275497762434, (44, 27212): 147.65640093978, (44, 27218): 146.7457644815564, (44, 27239): 149.19205074051771, (44, 27257): 148.3649047811774, (44, 27274): 149.4942340090664, (44, 27279): 149.29762815107927, (44, 27282): 148.38727809969683, (44, 27283): 148.7935957305364, (44, 27285): 149.8920583724328, (44, 27286): 149.01621228126322, (44, 27290): 147.60515081984676, (44, 27295): 147.08036056726218, (44, 27300): 149.66075846428618, (44, 27344): 147.11601390633876, (44, 27366): 148.12411031175364, (44, 27383): 149.92169335758553, (44, 27398): 151.0902177875493, (44, 27406): 150.2024215142413, (44, 27407): 150.49064667510154, (44, 27426): 149.4663569220618, (44, 27432): 145.47613294392303, (44, 27460): 147.9992587778901, (44, 27523): 148.09611769657573, (44, 27545): 164.61818100465393, (44, 27602): 185.15964526167596, (44, 27606): 185.55858348026806, (44, 27646): 163.64102850658028, (44, 27667): 167.76755171251517, (44, 27672): 167.99571346797072, (44, 27674): 167.2850161235205, (44, 27688): 167.921352236513, (44, 27692): 168.6959186465257, (44, 27693): 168.0757974227752, (44, 27705): 168.0301215884481, (44, 27712): 168.32396827317132, (44, 27786): 186.53694333352806, (44, 27790): 184.35761270694675, (44, 27791): 184.18371718411376, (44, 27795): 185.36380185949955, (44, 27801): 183.72571529584468, (44, 27813): 187.15758179759843, (44, 27816): 186.43240918907122, (44, 27823): 183.66508176793744, (44, 27830): 185.55266478502017, (44, 27884): 156.62072683289838, (44, 27885): 161.88711181544699, (44, 27896): 158.71030557056082, (44, 27919): 158.50447230401974, (44, 27922): 159.14118893865847, (44, 27930): 157.43722432544996, (44, 27934): 157.62776020614385, (44, 27935): 157.76399506190793, (44, 27948): 182.5066604905716, (44, 27951): 183.81582994516967, (44, 28061): 161.92087142803123, (44, 28290): 205.53718096644099, (44, 28292): 206.33702215471098, (44, 28293): 205.68559284043133, (44, 28295): 205.25218145142077, (44, 28296): 205.46062970919195, (44, 28297): 205.10585597232554, (44, 28302): 204.73710693421611, (44, 28310): 215.8895067824402, (44, 28313): 216.44895360467362, (44, 28372): 216.79642902865828, (44, 28398): 216.84967732148615, (44, 28399): 216.54845495827473, (44, 28400): 217.0073964619722, (44, 28401): 215.83144997226398, (44, 28445): 215.95482957293987, (44, 28475): 215.06901445985588, (44, 28885): 23.993176976412744, (44, 28886): 23.8423647608896, (44, 28915): 24.846954750118318, (44, 28916): 24.34253496561049, (44, 28917): 24.33885633296552, (44, 28921): 24.461812222150492, (44, 28931): 24.545355371467203, (44, 28945): 25.72495279463172, (44, 28982): 25.084185127132017, (44, 29219): 31.715025000525777, (44, 29228): 30.30816010285644, (44, 29246): 42.41932868013583, (44, 29248): 43.26135162035934, (44, 29282): 40.93775381638291, (44, 29290): 42.51309399352583, (44, 29291): 42.33129722504801, (44, 29292): 42.632672251309806, (44, 29293): 41.74664545441928, (44, 29294): 42.84416745283839, (44, 29298): 42.05951426597701, (44, 29299): 42.23648425047512, (44, 29304): 40.85803026086867, (44, 29317): 38.423638510392074, (44, 29323): 38.20638429254046, (44, 29330): 39.42122757784567, (44, 29331): 39.81533155403389, (44, 29344): 34.03016195854859, (44, 29445): 29.26560920020052, (44, 29724): 276.751603812752, (44, 29738): 277.110286205422, (44, 29745): 276.00103142735384, (44, 29748): 275.88866621616165, (44, 29750): 276.3404273780074, (44, 29759): 275.4360543816351, (44, 29772): 276.7566362809795, (44, 29781): 276.4591543501784, (44, 29784): 276.3698849019449, (44, 29790): 276.6904905131575, (44, 29811): 275.7971212538789, (44, 29817): 277.40507402339114, (44, 29818): 277.10993225592944, (44, 29929): 276.0741748857566, (44, 30039): 281.6212636632843, (44, 30066): 279.101047021606, (44, 30116): 266.2349385593585, (44, 30238): 247.210118576209, (44, 30248): 257.462605021422, (44, 30260): 257.7525509983927, (44, 30545): 16.407192871716763, (44, 30733): 12.5, (44, 30756): 15.371244668931457, (44, 30921): 12.5, (44, 31079): 59.36699542133003, (44, 31149): 57.9299032700686, (44, 31154): 58.411285768842546, (44, 31160): 57.97873308033149, (44, 31163): 58.64153581605155, (44, 31189): 64.03037690483737, (44, 31215): 64.08839869547589, (44, 31259): 66.95365076881075, (44, 31262): 67.40760309368117, (44, 31430): 60.769602013803045, (44, 31568): 80.4913978288579, (44, 31751): 63.5945936920975, (45, 109): 267.65065836854455, (45, 872): 130.47984523341228, (45, 873): 130.10026120793515, (45, 877): 129.78953445711159, (45, 879): 129.68908787070444, (45, 884): 129.0636720552607, (45, 889): 129.0364509049733, (45, 891): 129.3129099370659, (45, 892): 129.4899183663624, (45, 894): 129.72319334336686, (45, 896): 130.83918787311862, (45, 903): 129.25852703716382, (45, 909): 131.39190988544647, (45, 910): 131.65738206913977, (45, 912): 131.8115668185736, (45, 913): 131.83068055087122, (45, 916): 132.448804931166, (45, 926): 132.08421748962832, (45, 927): 132.30460506127753, (45, 948): 129.5264672311019, (45, 961): 131.11678851164535, (45, 962): 131.36621731357286, (45, 963): 131.5525633805405, (45, 967): 129.28153102000124, (45, 974): 128.43040523602474, (45, 998): 128.75889537927455, (45, 1014): 127.45146485508683, (45, 1086): 143.60169112258387, (45, 1087): 145.15123083297632, (45, 1089): 144.6647266141036, (45, 1090): 144.40234445361705, (45, 1092): 143.92832250094887, (45, 1097): 143.9918731625697, (45, 1107): 144.65412500213208, (45, 1387): 225.58090905200342, (45, 1554): 232.24615802871412, (45, 1827): 107.69591521340512, (45, 1828): 107.90808334708906, (45, 1829): 107.72930992728723, (45, 1830): 106.68046797583857, (45, 1831): 106.85779447908762, (45, 1832): 106.97808731075607, (45, 1833): 107.16035152138433, (45, 1836): 107.38540929253729, (45, 1841): 107.01666704897788, (45, 1843): 107.05749349215232, (45, 1844): 106.85656557018956, (45, 1845): 106.74510891562653, (45, 1847): 107.44819001937856, (45, 1848): 107.32484806569637, (45, 1849): 106.57563125416829, (45, 1850): 106.68739022376012, (45, 1851): 106.74193348225053, (45, 1852): 106.31033767149694, (45, 1854): 106.58718039652331, (45, 1856): 106.90444439370846, (45, 1857): 107.10156843032884, (45, 1858): 106.92429197168282, (45, 1861): 107.37054448746647, (45, 1866): 106.54554975508509, (45, 1867): 107.37240699175089, (45, 1868): 107.75250761697177, (45, 1870): 106.31394785270163, (45, 1871): 107.73754072527545, (45, 1875): 106.87937217630554, (45, 1880): 107.21339680000698, (45, 1882): 106.57574885500148, (45, 1883): 107.16729136368565, (45, 1889): 107.87004609499297, (45, 1893): 108.41944764301486, (45, 1894): 108.59078939387707, (45, 1899): 108.20645253058606, (45, 1900): 108.3132672210758, (45, 1902): 108.33341557217558, (45, 1905): 107.9919530216082, (45, 1907): 107.70109190924148, (45, 1910): 108.20148254252145, (45, 1917): 109.25209514205004, (45, 1920): 108.07035092415944, (45, 1935): 108.80163129010437, (45, 1937): 108.6093550293122, (45, 1946): 109.28021139539867, (45, 1949): 109.44745239037691, (45, 1950): 108.55183811907851, (45, 1951): 108.74889988091817, (45, 1952): 107.59229791440666, (45, 1953): 108.57957541575922, (45, 1954): 107.8751792621739, (45, 1958): 109.00269138798292, (45, 1960): 108.65228743101306, (45, 1968): 108.51699597410872, (45, 1969): 109.61691821058004, (45, 1974): 109.25291156411431, (45, 1975): 108.97648360837023, (45, 1979): 109.58611688134681, (45, 1980): 108.76485712105622, (45, 1981): 109.26580863584952, (45, 1985): 109.4805574610941, (45, 1994): 106.71336581650291, (45, 2011): 106.29598339045707, (45, 2019): 104.85313699109729, (45, 2020): 105.03510184696874, (45, 2029): 104.92974664008045, (45, 2030): 105.17464837246435, (45, 2032): 104.49864978082438, (45, 2033): 104.95768768591877, (45, 2034): 104.55140955767142, (45, 2036): 102.91217801556428, (45, 2037): 103.39470035653609, (45, 2038): 105.29318791318808, (45, 2042): 104.50074222834432, (45, 2050): 105.58595674393493, (45, 2051): 105.1595827042869, (45, 2053): 105.33011514634408, (45, 2054): 105.24263654456418, (45, 2066): 105.34443078677286, (45, 2067): 105.56827830179697, (45, 2071): 107.07643182932796, (45, 2072): 107.27484963341178, (45, 2073): 108.73159522846589, (45, 2074): 108.47252461826093, (45, 2080): 107.99172206665489, (45, 2082): 107.28560701358926, (45, 2083): 107.41693165217413, (45, 2089): 107.83498269053035, (45, 2090): 108.03077748494484, (45, 2092): 108.33575631553732, (45, 2098): 108.46904973544342, (45, 2099): 108.1499325092882, (45, 2101): 108.10171259492567, (45, 2102): 108.32132217838604, (45, 2103): 108.09485834988102, (45, 2104): 107.79239389777237, (45, 2106): 107.2163700585682, (45, 2112): 107.77533086265349, (45, 2113): 108.11974165346942, (45, 2114): 107.51595653229086, (45, 2117): 106.91357495081526, (45, 2123): 121.86819868755424, (45, 2124): 121.92604520409463, (45, 2134): 120.75153461739508, (45, 2138): 121.32279701662299, (45, 2141): 121.08207362678134, (45, 2148): 117.23687189525468, (45, 2150): 120.76267432420043, (45, 2151): 120.53108483509034, (45, 2152): 120.46677177836675, (45, 2153): 117.62930219139791, (45, 2154): 117.65953368107947, (45, 2155): 116.97390322356634, (45, 2156): 117.40979596759891, (45, 2157): 115.04644466612557, (45, 2160): 119.50950510182057, (45, 2161): 120.0691090917517, (45, 2162): 116.14961706920761, (45, 2163): 116.20838427919337, (45, 2164): 115.96513349042293, (45, 2168): 118.77340016672527, (45, 2172): 117.02381238458501, (45, 2174): 120.03129785654784, (45, 2178): 116.53790781667371, (45, 2179): 116.35678544816665, (45, 2183): 120.86407233177869, (45, 2185): 120.62472608937429, (45, 2186): 120.7082524821094, (45, 2190): 119.95073210479558, (45, 2192): 120.01633126049984, (45, 2193): 121.01602228009627, (45, 2194): 121.0820055777151, (45, 2195): 120.5710671386923, (45, 2197): 119.74706189999962, (45, 2205): 119.10593660680124, (45, 2207): 118.44303293405571, (45, 2208): 118.7091389420649, (45, 2212): 122.13989112189111, (45, 2214): 114.60049873531268, (45, 2225): 113.0325068644246, (45, 2231): 124.10276457080371, (45, 2278): 109.24039731106689, (45, 2284): 108.30971604089842, (45, 2285): 107.9809241980478, (45, 2291): 105.9174755356905, (45, 2292): 108.61939921463919, (45, 2307): 108.302278671054, (45, 2313): 105.09489391794538, (45, 2317): 109.80265350010751, (45, 2319): 108.31328715285463, (45, 2321): 107.81284946841448, (45, 2323): 108.58839022891364, (45, 2326): 109.84982658260246, (45, 2327): 109.89297162686144, (45, 2329): 109.84376333861842, (45, 2330): 109.60696922961958, (45, 2332): 109.1702955692137, (45, 2344): 110.395910531575, (45, 2346): 109.86048941387443, (45, 2361): 114.37102818323812, (45, 2368): 111.34597987442345, (45, 2374): 110.8942406845569, (45, 2375): 111.15458349750354, (45, 2377): 111.6873841797291, (45, 2378): 110.89989352134734, (45, 2379): 110.34992851416155, (45, 2380): 110.72439129794897, (45, 2383): 111.97788664520499, (45, 2385): 112.1448127784129, (45, 2395): 112.62601714802322, (45, 2397): 110.12026653956528, (45, 2398): 111.8014290783399, (45, 2399): 111.98528768806483, (45, 2400): 112.01160692131008, (45, 2402): 110.38342784316062, (45, 2403): 110.30409560830192, (45, 2404): 110.50735588047158, (45, 2405): 110.49864358843556, (45, 2407): 110.82912189084286, (45, 2408): 110.50602180304507, (45, 2409): 110.58570766336076, (45, 2411): 109.3977256099469, (45, 2412): 109.75854320712341, (45, 2413): 109.56946252794643, (45, 2414): 109.55149159364436, (45, 2422): 109.10538922116986, (45, 2424): 109.93530900617372, (45, 2426): 110.10302887167724, (45, 2433): 109.88829380117586, (45, 2436): 109.332400344374, (45, 2437): 109.95775250123015, (45, 2440): 109.97802163068917, (45, 2445): 103.39508382593851, (45, 2447): 104.07572030412946, (45, 2454): 103.94072080167713, (45, 2455): 104.37213165089523, (45, 2460): 104.24144180129544, (45, 2461): 104.15587940351476, (45, 2471): 100.99525705904126, (45, 2492): 84.71605452283131, (45, 2511): 88.06705223752819, (45, 2523): 86.27902490273567, (45, 2525): 85.43784764610355, (45, 2535): 94.30217551820714, (45, 2537): 94.11958114916608, (45, 2538): 94.6799676774908, (45, 2539): 92.55738023940008, (45, 2540): 94.33238079683017, (45, 2542): 93.71854592552303, (45, 2559): 98.42479072152726, (45, 2575): 95.75536148839161, (45, 2599): 102.01104093078013, (45, 2600): 100.3182744062988, (45, 2607): 102.92983222413221, (45, 2627): 80.19552345949599, (45, 2647): 78.50168304611034, (45, 2674): 80.93755437887901, (45, 2681): 79.84571286814236, (45, 2683): 80.24102002840445, (45, 2686): 80.91527177889334, (45, 2689): 79.35452482847263, (45, 2690): 79.08301616577054, (45, 2713): 71.08616393325356, (45, 2714): 70.00321014761694, (45, 2715): 70.08751084973206, (45, 2739): 70.33718598121722, (45, 2740): 72.92109763519393, (45, 2741): 73.17555835732536, (45, 2749): 69.06578706513758, (45, 2750): 69.48090907262532, (45, 2752): 69.71605381584381, (45, 2755): 69.53379551507379, (45, 2758): 69.18688574487233, (45, 2759): 69.36253201157477, (45, 2769): 69.71466404602212, (45, 2771): 72.23466500737759, (45, 2779): 69.40568466712561, (45, 2784): 67.50384041897897, (45, 2800): 64.80376648266817, (45, 2802): 71.27181929325175, (45, 2803): 71.60583248744835, (45, 2804): 71.70771224379884, (45, 2805): 70.24589902207506, (45, 2807): 70.60323502123249, (45, 2809): 69.77477018884508, (45, 2812): 70.33580681738198, (45, 2814): 67.37018934642316, (45, 2817): 64.17284388492659, (45, 2819): 71.4956020141101, (45, 2823): 67.2497906641601, (45, 2832): 69.81130145567634, (45, 2836): 69.59983553448784, (45, 2839): 70.96877699212185, (45, 2841): 65.81119118389833, (45, 2843): 66.36835346002617, (45, 2846): 68.18489391391272, (45, 2849): 69.23939399380822, (45, 2852): 69.4177949173314, (45, 2853): 69.13569513586204, (45, 2876): 67.4849733474182, (45, 2877): 67.4425317260651, (45, 2885): 64.11751027516038, (45, 2918): 73.83369906458019, (45, 2921): 73.4752540828604, (45, 2925): 76.35927652919808, (45, 2926): 78.01189663505978, (45, 2930): 72.4355561858754, (45, 2931): 75.38562932586666, (45, 2938): 73.20583530163073, (45, 2940): 76.37944875584509, (45, 2947): 76.93178726698872, (45, 2949): 73.85653662504036, (45, 2950): 73.26561311867682, (45, 2952): 73.21797234050659, (45, 2958): 73.46706033639823, (45, 2959): 74.21155662925845, (45, 2960): 74.03945321147484, (45, 2961): 73.72313737558946, (45, 2963): 73.0845214356896, (45, 2968): 72.7349319139288, (45, 2976): 73.45265324103623, (45, 2981): 68.54718174429398, (45, 2982): 67.80081260846706, (45, 2984): 67.61095416462041, (45, 3003): 66.7638075597147, (45, 3046): 74.96926663990989, (45, 3050): 71.12316593947328, (45, 3051): 71.41680325990532, (45, 3053): 71.0708156603572, (45, 3069): 70.1152564839734, (45, 3071): 72.74175882757025, (45, 3080): 62.90305078835359, (45, 3199): 62.23327781935504, (45, 3200): 61.685599886154506, (45, 3205): 62.529765384535025, (45, 3209): 61.631487740053366, (45, 3215): 62.091517494101616, (45, 3217): 61.91841189011926, (45, 3249): 62.53117489204544, (45, 3263): 64.28475991661207, (45, 3289): 64.11988249813254, (45, 3301): 63.11930491926508, (45, 3302): 63.43390563232315, (45, 3307): 63.45755443232678, (45, 3310): 63.20475429266165, (45, 3391): 43.44813397910033, (45, 3509): 128.05472776006084, (45, 3510): 128.4712578437662, (45, 3511): 128.43388223472203, (45, 3512): 128.90171337838717, (45, 3514): 129.0065582228693, (45, 3519): 125.91302494573749, (45, 3536): 127.74951900164749, (45, 3545): 127.3522033574553, (45, 3548): 128.30481691873703, (45, 3572): 127.21890563425777, (45, 3581): 126.92306917068258, (45, 3583): 128.1919332766105, (45, 3601): 124.75940773981407, (45, 3656): 124.56271421322215, (45, 3669): 123.58987548382203, (45, 3670): 123.12315569163287, (45, 3695): 126.0968833437605, (45, 3696): 125.81884259624205, (45, 3782): 132.66665593299518, (45, 3792): 132.38259088503168, (45, 3989): 319.62688740523606, (45, 4008): 321.7737427002285, (45, 4031): 320.7857677475196, (45, 4045): 320.8320595846852, (45, 4144): 321.74016468486644, (45, 4145): 320.4324429181595, (45, 4164): 321.110900422401, (45, 4168): 320.83839020173104, (45, 4173): 320.8996944110746, (45, 4181): 319.58293995146755, (45, 4228): 317.44394668213675, (45, 4248): 318.1142814578748, (45, 4254): 309.8935678421631, (45, 4260): 309.5664239535681, (45, 4262): 310.56864598490563, (45, 4273): 310.16468264004516, (45, 4319): 304.8480050257352, (45, 4326): 304.53154571563744, (45, 4328): 304.5282932195381, (45, 4334): 305.2471395265322, (45, 4335): 305.1401481611564, (45, 4372): 316.24246036893146, (45, 4413): 325.0015883414664, (45, 4434): 315.847218624888, (45, 4447): 316.8841413542737, (45, 4452): 315.9838903157454, (45, 4463): 298.8119586566482, (45, 4465): 299.3835240621396, (45, 4619): 326.192450252276, (45, 4645): 328.0544537112793, (45, 4657): 327.7733186031791, (45, 4666): 327.0541774202379, (45, 4676): 328.37031117990415, (45, 4678): 328.6572669843793, (45, 4689): 327.77635713273736, (45, 4704): 334.31187657559, (45, 4726): 349.9741740090888, (45, 4727): 349.6864216471416, (45, 4730): 349.1306277383419, (45, 4731): 349.2740683767629, (45, 4734): 349.6786279370748, (45, 4735): 349.3924735299942, (45, 4736): 349.51866225660564, (45, 4737): 349.0185610051184, (45, 4738): 349.0737860850031, (45, 4756): 349.3545155544302, (45, 4760): 347.97347652282934, (45, 4761): 348.1620476799925, (45, 4762): 347.56350370368637, (45, 4765): 348.1078607889167, (45, 4773): 350.554453099513, (45, 4774): 350.267430015526, (45, 4790): 350.3677773256495, (45, 4795): 350.1239199894985, (45, 4799): 350.375580820322, (45, 4801): 350.9351470839404, (45, 4804): 350.2589921899708, (45, 4805): 350.05795373062836, (45, 4806): 350.11296882897483, (45, 4815): 349.8101646466631, (45, 4816): 350.54441976245005, (45, 4817): 350.6505196385058, (45, 4826): 350.2330571208942, (45, 4830): 349.8093382341254, (45, 4839): 348.8119004869124, (45, 4840): 349.05537571710687, (45, 4841): 348.43688997082273, (45, 4846): 348.24249169331756, (45, 4848): 348.149355883781, (45, 4850): 348.40644357268275, (45, 4871): 345.17980748238904, (45, 4883): 347.68747848631494, (45, 4900): 346.4342704531857, (45, 4901): 346.0547145892049, (45, 4917): 325.61382910796294, (45, 4931): 323.47104169617876, (45, 4944): 325.8785622111195, (45, 4956): 323.8423061901873, (45, 4958): 323.7368518028509, (45, 4959): 323.30013012062284, (45, 4961): 324.2938177307728, (45, 4966): 323.29357306439954, (45, 5207): 320.9146886257695, (45, 5272): 280.10716028349174, (45, 5283): 280.9113933648594, (45, 5287): 282.1940136686189, (45, 5289): 282.5453871510225, (45, 5293): 280.24648021226955, (45, 5295): 282.49842614534214, (45, 5296): 282.48516733848055, (45, 5298): 282.45953525866514, (45, 5303): 283.1229263940779, (45, 5305): 279.6489749243776, (45, 5306): 279.0282495537869, (45, 5307): 279.2329077945302, (45, 5308): 280.0184624623869, (45, 5313): 279.9812442429386, (45, 5314): 280.48637797828263, (45, 5317): 280.0243843120317, (45, 5319): 282.3505217127335, (45, 5324): 281.8967711198271, (45, 5326): 281.60386013051897, (45, 5348): 278.84329775830065, (45, 5351): 279.43473395607583, (45, 5399): 282.9948603515441, (45, 5413): 280.4451135395356, (45, 5422): 283.4297033868895, (45, 5445): 281.600419380293, (45, 5448): 280.83813127364397, (45, 5456): 280.6583808355916, (45, 5467): 281.36566511654775, (45, 5624): 272.95282722111375, (45, 5671): 297.77184370356355, (45, 5672): 296.71913032902154, (45, 5797): 310.2516185256819, (45, 5871): 293.5228905569995, (45, 5976): 284.6211382989178, (45, 6118): 59.235909957110806, (45, 6248): 43.60211186240147, (45, 6345): 224.82209122326074, (45, 6352): 222.2505443369216, (45, 6354): 225.5278528862385, (45, 6359): 225.89902503215365, (45, 6376): 222.32630395791375, (45, 6378): 225.2071962645915, (45, 6381): 225.5939278491988, (45, 6383): 224.33141224902067, (45, 6396): 224.77234210645045, (45, 6399): 224.69010490431089, (45, 6408): 222.48106052049516, (45, 6409): 224.05912393164775, (45, 6419): 220.5053598229234, (45, 6422): 223.10795466984436, (45, 6423): 222.92124523444448, (45, 6424): 225.6905476561018, (45, 6439): 225.31890553621747, (45, 6464): 224.72590203874142, (45, 6465): 224.33953028482583, (45, 6469): 224.38838122055756, (45, 6470): 224.16892546656268, (45, 6472): 226.71730142129374, (45, 6480): 226.7977401804277, (45, 6486): 229.00790352347113, (45, 6497): 228.29675320709944, (45, 6503): 225.68898129925256, (45, 6508): 225.43513644729092, (45, 6509): 226.12857995559202, (45, 6521): 227.4046707020357, (45, 6544): 227.63993829586147, (45, 6552): 224.23243426183475, (45, 6553): 223.87708364785806, (45, 6554): 223.51008160178142, (45, 6578): 224.76665024347554, (45, 6582): 224.92794757275803, (45, 6601): 225.0214851250882, (45, 6609): 227.54066558916193, (45, 6610): 227.73531167357132, (45, 6611): 227.57973526233567, (45, 6614): 227.2500547896608, (45, 6615): 227.39789779413135, (45, 6616): 228.0844775254681, (45, 6617): 227.80849060195402, (45, 6618): 228.66320802631876, (45, 6619): 227.02426401394675, (45, 6620): 228.23659844268386, (45, 6621): 227.9483890131605, (45, 6622): 227.92262571684418, (45, 6623): 227.36994866445986, (45, 6624): 227.23571986737255, (45, 6625): 227.0989636660573, (45, 6626): 226.9449866501802, (45, 6627): 227.04925264020963, (45, 6628): 228.31868655983783, (45, 6629): 227.50070716843877, (45, 6630): 226.59797761979004, (45, 6632): 227.38803092830202, (45, 6634): 226.34417217325355, (45, 6635): 227.75588512474283, (45, 6636): 228.15214656121728, (45, 6637): 227.0799693979311, (45, 6638): 226.77143814679837, (45, 6639): 227.16385832087903, (45, 6640): 226.75344452098395, (45, 6641): 228.05414682128458, (45, 6642): 226.87357232864693, (45, 6643): 226.8090576155017, (45, 6645): 227.13307239696, (45, 6646): 228.43496419480041, (45, 6647): 226.91689933999908, (45, 6653): 227.34004352707476, (45, 6655): 227.12200801860433, (45, 6658): 226.37596544090658, (45, 6662): 226.9575133881298, (45, 6819): 210.91953467425486, (45, 6996): 219.57695455209605, (45, 7059): 223.6505838752378, (45, 7187): 223.20178590622024, (45, 7304): 210.69235243251507, (45, 7528): 221.92202330615012, (45, 7720): 244.04695117668788, (45, 7793): 244.51243349575094, (45, 7807): 244.52935123625468, (45, 7808): 244.61842830796655, (45, 7831): 230.86138149476406, (45, 7850): 234.12185127736416, (45, 7852): 233.00379229372393, (45, 8012): 241.55888441232955, (45, 8125): 251.80106673810192, (45, 8208): 251.79677361649468, (45, 8392): 236.39343687862223, (45, 8651): 191.42816662432315, (45, 9088): 206.4997655363306, (45, 9443): 192.88822284226094, (45, 9444): 193.6167732530673, (45, 9828): 182.16369340933272, (45, 9868): 176.09905132524113, (45, 10180): 252.65906788757238, (45, 10256): 263.61692994811676, (45, 10276): 257.760369664075, (45, 10378): 256.52185897097456, (45, 10676): 253.23700322121422, (45, 10714): 247.50436837303403, (45, 10730): 245.61776557361793, (45, 10862): 266.1307526437877, (45, 10881): 267.8280976217967, (45, 10883): 267.66907704833426, (45, 10885): 265.75835041025397, (45, 10891): 267.42563231010416, (45, 10909): 267.2072302437885, (45, 10911): 267.37397435726643, (45, 10913): 267.0052429465461, (45, 10915): 266.9507748813265, (45, 10919): 267.1561003717369, (45, 11037): 256.6756548010683, (45, 11039): 252.0131398623591, (45, 11516): 334.20869134637724, (45, 11856): 305.49920301408537, (45, 11857): 305.52444939791127, (45, 11861): 305.5348430394838, (45, 11881): 304.58638141018963, (45, 11902): 302.8076540279929, (45, 11911): 302.09088660086877, (45, 11914): 302.51042246047064, (45, 11922): 303.9690512343979, (45, 11924): 304.2868290890462, (45, 11926): 303.75110418984417, (45, 11950): 304.3266236128566, (45, 11963): 306.06325513444926, (45, 11983): 304.19091964286065, (45, 11985): 306.9712113137223, (45, 12009): 306.0199405963735, (45, 12010): 304.9434946635969, (45, 12018): 305.06204618946254, (45, 12020): 305.4843421761139, (45, 12021): 305.619331222572, (45, 12024): 306.7906552623427, (45, 12025): 306.521064414431, (45, 12027): 306.2124490874355, (45, 12031): 304.7421463951288, (45, 12032): 305.2473879688086, (45, 12035): 305.79876581337794, (45, 12041): 307.47842703272016, (45, 12045): 290.64250031049005, (45, 12145): 297.4407831935245, (45, 12275): 318.88572703802544, (45, 12294): 314.9725768121126, (45, 12358): 323.8715718381755, (45, 12463): 326.81849590654446, (45, 12465): 326.6600835899317, (45, 12482): 329.00234742050816, (45, 12503): 328.5995226944549, (45, 12506): 329.0670474609381, (45, 12549): 328.8685205811087, (45, 12559): 328.34937497301996, (45, 12569): 328.44435214547684, (45, 12572): 328.8126601626973, (45, 12574): 328.13277458816026, (45, 12576): 329.3735784842671, (45, 12591): 329.7562464393472, (45, 12608): 332.9611407955362, (45, 12696): 328.68181532724964, (45, 12710): 331.9817139477529, (45, 12728): 330.01073426324626, (45, 12766): 256.53056707372207, (45, 12771): 255.05905482068823, (45, 12790): 254.579762103999, (45, 12795): 253.2696410969454, (45, 12797): 250.3474228753669, (45, 12798): 250.95067208067147, (45, 12811): 253.9791504196623, (45, 12830): 252.6450338329045, (45, 12848): 253.8187193251318, (45, 12850): 254.46276491890725, (45, 12852): 252.69259391009587, (45, 12854): 252.22145478096581, (45, 12859): 254.45688737906892, (45, 12861): 251.61515277939571, (45, 12865): 254.27622640844768, (45, 12866): 254.22192688873454, (45, 12867): 254.99844086974528, (45, 12874): 254.5952772594831, (45, 12875): 255.03348958059487, (45, 12881): 253.3516717883416, (45, 12883): 253.95769396559072, (45, 12885): 255.30102350794118, (45, 12888): 253.81110544436956, (45, 12889): 253.80232413069942, (45, 12892): 254.62429176655817, (45, 12893): 253.70313908384972, (45, 12896): 254.11637967686212, (45, 12906): 254.0542975965698, (45, 13018): 246.45749914770872, (45, 13071): 245.78836893622073, (45, 13131): 244.8018043075605, (45, 13146): 248.59983745756375, (45, 13159): 240.43434392349576, (45, 13193): 244.39838041774354, (45, 13198): 240.0471400683641, (45, 13292): 246.8242642762393, (45, 13296): 249.9818622709652, (45, 13406): 234.49255184565317, (45, 13407): 234.14545243326708, (45, 13417): 232.44332579093373, (45, 13418): 232.84967023264863, (45, 13438): 236.32915209651728, (45, 13442): 237.24652436505372, (45, 13443): 236.71295963876318, (45, 13764): 185.41480463492815, (45, 13766): 186.07896193441744, (45, 13771): 185.0206091451463, (45, 13783): 185.5579095795412, (45, 13784): 186.98117271053644, (45, 13792): 183.12828308225963, (45, 13824): 185.0192250136292, (45, 14017): 191.41725219563406, (45, 14870): 264.5593470933296, (45, 14997): 220.83907210409478, (45, 15000): 221.2311818500777, (45, 15003): 221.9842999405602, (45, 15006): 221.47621171062343, (45, 15007): 221.9375650758172, (45, 15056): 222.8666724010628, (45, 15063): 222.6804220744583, (45, 15069): 222.91640591303934, (45, 15076): 222.23678009433627, (45, 15086): 220.47594591289194, (45, 15087): 220.47305349010517, (45, 15111): 218.86282551947295, (45, 15116): 219.82080145299685, (45, 15722): 208.28294425973942, (45, 15998): 209.90193385988218, (45, 16073): 88.37074961619108, (45, 16939): 99.06979709741465, (45, 16940): 99.44053716929416, (45, 16951): 97.65308406920752, (45, 16963): 97.9544496415499, (45, 16965): 98.10777961377727, (45, 16969): 97.35543825068369, (45, 16970): 98.27474035944111, (45, 16971): 98.19011183331793, (45, 16973): 97.69431192863658, (45, 16974): 97.69795084079257, (45, 16976): 98.59368248114252, (45, 16978): 98.70216049592021, (45, 16980): 99.04788257693357, (45, 16982): 97.1817384442535, (45, 17045): 57.11438132245707, (45, 17048): 57.018961788491154, (45, 17304): 315.97245336404393, (45, 17305): 315.0482791992978, (45, 17330): 315.60376083398677, (45, 17334): 315.2495693126385, (45, 17343): 316.11162498959163, (45, 17345): 314.68887482580675, (45, 17347): 315.20092906447275, (45, 17351): 314.1455871654776, (45, 17372): 314.9581865389612, (45, 17373): 316.1449306237411, (45, 17377): 316.1847601763998, (45, 17382): 315.29969642763126, (45, 17383): 315.64214166556053, (45, 17389): 315.0767325901082, (45, 17400): 316.0649784360803, (45, 17401): 316.13150999658626, (45, 17402): 316.06616012892005, (45, 17403): 316.11141366189884, (45, 17440): 314.1667021875363, (45, 17455): 315.60579782065344, (45, 17491): 315.2967618752314, (45, 17507): 315.93760563721077, (45, 17509): 316.5862112468188, (45, 17590): 313.2105023828016, (45, 17615): 313.74285793072335, (45, 17642): 313.9963448146688, (45, 17643): 313.74937331620396, (45, 17668): 313.848553813465, (45, 17721): 313.7651762287945, (45, 17754): 318.9881586817371, (45, 17769): 316.70966441028685, (45, 17776): 313.6875019262046, (45, 17804): 317.6467198561206, (45, 17809): 318.1703736935295, (45, 17824): 318.162727390551, (45, 17837): 315.08042292327883, (45, 17838): 314.8375477033219, (45, 17862): 314.3061180829876, (45, 17866): 315.559728669414, (45, 17872): 314.113318216513, (45, 17873): 313.0887339538931, (45, 17881): 314.6164168044966, (45, 17947): 143.5608666236112, (45, 17951): 143.50312291306597, (45, 17953): 143.8801935143021, (45, 17954): 144.13671388460327, (45, 17959): 142.87942900766694, (45, 17963): 142.18895654683595, (45, 18000): 143.2624797259484, (45, 18001): 143.74321599899736, (45, 18111): 161.32358041879104, (45, 18148): 165.78196735518512, (45, 18166): 165.37624950358583, (45, 18189): 161.45021359945326, (45, 18239): 316.6108666319277, (45, 18240): 316.5417234739335, (45, 18245): 316.6270208111578, (45, 18247): 316.4459414655423, (45, 18251): 316.5484376001723, (45, 18256): 316.5861557381226, (45, 18258): 316.41903426384914, (45, 18259): 316.4086395847021, (45, 18260): 316.4119113217601, (45, 18262): 316.46455305037983, (45, 18263): 316.58456393649885, (45, 18264): 316.5918541746744, (45, 18266): 316.4471440115646, (45, 18267): 316.46314210443984, (45, 18268): 316.44743421999465, (45, 18269): 316.4725698317646, (45, 18275): 316.4604285621483, (45, 18285): 316.6142405757968, (45, 18308): 316.3430177416975, (45, 18313): 316.07348470620485, (45, 18314): 316.0005836440842, (45, 18315): 316.6458071816692, (45, 18316): 316.55708370581505, (45, 18317): 316.56351943989415, (45, 18320): 316.6920480500637, (45, 18321): 316.65742185522953, (45, 18322): 316.6847610307594, (45, 18324): 316.8276853877774, (45, 18325): 317.0302474714857, (45, 18326): 316.95866793426126, (45, 18327): 316.49868440626875, (45, 18329): 317.21567468861724, (45, 18330): 316.85131010900153, (45, 18331): 316.75735903959514, (45, 18332): 316.61692652890883, (45, 18333): 316.90541162367697, (45, 18336): 316.9181782984881, (45, 18337): 317.0409543268392, (45, 18403): 316.46316339021985, (45, 18432): 311.24971275934496, (45, 18451): 314.7675114504944, (45, 18466): 318.4327329401573, (45, 18481): 316.9220434712749, (45, 18483): 316.86250021796104, (45, 18484): 316.7965934958755, (45, 18485): 316.65825448300143, (45, 18486): 317.1688450673418, (45, 18487): 316.981158682816, (45, 18489): 316.93665722313193, (45, 18490): 317.3566207206197, (45, 18491): 317.47893657302865, (45, 18492): 316.6702577368851, (45, 18493): 317.1960999971202, (45, 18494): 316.83894576991315, (45, 18495): 317.2743737121433, (45, 18496): 317.097516362657, (45, 18497): 316.99270733764826, (45, 18498): 316.81115034895123, (45, 18499): 316.9792662298823, (45, 18501): 316.96231218659653, (45, 18502): 316.86152188919465, (45, 18503): 316.71204881968674, (45, 18504): 317.07497818436065, (45, 18506): 317.14863437363914, (45, 18507): 317.0861287846923, (45, 18508): 317.01336248232565, (45, 18509): 317.0717338023527, (45, 18510): 316.79757285284484, (45, 18511): 317.3494829095163, (45, 18512): 317.10933085537994, (45, 18515): 317.1694214495286, (45, 18516): 317.3727113851481, (45, 18517): 317.33005723030266, (45, 18518): 317.41016822373086, (45, 18519): 317.06421092267135, (45, 18520): 316.9105672428995, (45, 18522): 317.413174487165, (45, 18523): 317.5028432642924, (45, 18532): 317.75255556644316, (45, 18535): 317.3002094409302, (45, 18537): 317.048433831579, (45, 18539): 317.13480319398155, (45, 18540): 317.1997610103659, (45, 18541): 317.3531658103571, (45, 18542): 317.44442443597785, (45, 18543): 317.0175101936151, (45, 18546): 317.32981017781555, (45, 18555): 317.7306006452684, (45, 18556): 317.8474356025222, (45, 18565): 317.810096035894, (45, 18567): 318.05362748334204, (45, 18568): 317.78101931833334, (45, 18577): 319.32159880853686, (45, 18583): 318.8858078050487, (45, 18605): 318.99675965050585, (45, 18608): 318.44363201659564, (45, 18616): 320.44885023203733, (45, 18618): 321.79836980519894, (45, 18625): 320.90462517749484, (45, 18645): 319.622434503166, (45, 18646): 320.0614972831441, (45, 18653): 319.4837725399571, (45, 18654): 320.49422790983516, (45, 18655): 319.92657778631934, (45, 18666): 323.1419825784506, (45, 18837): 311.82968230587664, (45, 18974): 313.2589077520433, (45, 18999): 313.4907459425733, (45, 19000): 313.8417191004975, (45, 19174): 293.16083365653657, (45, 19342): 298.97161818500416, (45, 19455): 298.68893072988925, (45, 19555): 279.7565542239156, (45, 19564): 279.23890322549624, (45, 19573): 278.8369417336889, (45, 19586): 278.7569851903905, (45, 19605): 279.2738433709783, (45, 19611): 279.6038678965343, (45, 19614): 279.87007395693695, (45, 19641): 287.2835721894953, (45, 19702): 286.67612762000107, (45, 19713): 286.2303372955728, (45, 19731): 279.22134130580355, (45, 19819): 295.08466874537174, (45, 19893): 296.09337367928555, (45, 19899): 300.86859827713903, (45, 19929): 297.1393874504563, (45, 19951): 305.9052825834424, (45, 19962): 298.25148923552047, (45, 19970): 299.3728206961657, (45, 19971): 299.59963832324536, (45, 19972): 298.9977319791442, (45, 19975): 298.519973575307, (45, 19978): 306.9492666546719, (45, 19987): 306.98010983894716, (45, 19989): 304.5748241498704, (45, 20039): 307.36444897953714, (45, 20043): 308.2047992143734, (45, 20047): 307.29006835903436, (45, 20052): 304.76300129488146, (45, 20054): 305.0510125008008, (45, 20085): 316.01095346382743, (45, 20104): 316.72727738002504, (45, 20132): 312.5049160270186, (45, 20203): 297.28828150724024, (45, 20280): 296.82677648569035, (45, 20285): 296.79351716729474, (45, 20290): 297.14302876357965, (45, 20297): 296.2978339034494, (45, 20309): 308.7905083947192, (45, 20453): 320.01142361195156, (45, 20485): 291.0299295319828, (45, 20520): 288.8619904369548, (45, 20526): 288.6371411240904, (45, 20698): 160.32021525952288, (45, 20868): 136.0893656440096, (45, 21042): 262.0850717934762, (45, 21057): 266.18203546376634, (45, 21066): 264.54706715493626, (45, 21075): 263.2347736040552, (45, 21093): 262.91709684391753, (45, 21098): 266.59315951289227, (45, 21127): 262.7008494035985, (45, 21130): 263.73149444540996, (45, 21144): 263.1212156264127, (45, 21146): 262.4300679446266, (45, 21147): 262.9045824883778, (45, 21148): 263.792387722839, (45, 21153): 260.1597893017867, (45, 21293): 269.584830537377, (45, 21426): 263.8032896660271, (45, 21442): 267.3597490092904, (45, 21451): 267.72553327871395, (45, 21466): 265.8190748685155, (45, 21469): 266.5773300110184, (45, 21471): 265.42436691931505, (45, 21473): 266.10841824753106, (45, 21475): 265.5599505704431, (45, 21482): 266.86559751082, (45, 21484): 266.8082526184914, (45, 21488): 266.3115857484426, (45, 21494): 265.8207742690732, (45, 21498): 266.31794263291187, (45, 21500): 265.7407785400166, (45, 21514): 268.12977676628174, (45, 21537): 266.1827571458514, (45, 21662): 269.4489703037752, (45, 21691): 266.70976974416243, (45, 21757): 259.83634277386295, (45, 21777): 255.7811199434475, (45, 21778): 255.10002078059046, (45, 21779): 255.7267434387326, (45, 21790): 256.2821194597902, (45, 21802): 256.7274659656867, (45, 21824): 257.6795033262998, (45, 21874): 256.20561199248704, (45, 21879): 256.2562394464831, (45, 21983): 256.6465651816797, (45, 22002): 265.66907661913064, (45, 22132): 255.35308494981348, (45, 22261): 191.1586046749991, (45, 22298): 193.28179804067074, (45, 22339): 191.61041222524398, (45, 22508): 199.9110437107543, (45, 22841): 12.5, (45, 22842): 12.5, (45, 22874): 12.5, (45, 22941): 12.5, (45, 22956): 12.5, (45, 22960): 12.5, (45, 22968): 12.5, (45, 22970): 12.5, (45, 22974): 12.5, (45, 22980): 12.5, (45, 23025): 13.292812413998977, (45, 23028): 14.154664025788328, (45, 23081): 20.840262524939888, (45, 23104): 28.36066288855243, (45, 23147): 15.398260001002289, (45, 23298): 281.469786229566, (45, 23376): 279.5930373796188, (45, 23381): 279.6254142534478, (45, 23529): 283.6129931576929, (45, 23556): 282.3785986950065, (45, 23718): 279.35563149737055, (45, 24001): 292.3913380667897, (45, 24094): 297.86135450839527, (45, 24129): 299.74828997687956, (45, 24174): 296.617206465393, (45, 24235): 301.33332054741516, (45, 24259): 302.62218500689573, (45, 24260): 302.5657583648661, (45, 24261): 302.084732718436, (45, 24305): 304.5663182816417, (45, 24306): 305.0385552771491, (45, 24307): 304.4246577448271, (45, 24308): 295.7527259954642, (45, 24498): 307.77340104202284, (45, 24499): 307.85310697339764, (45, 24500): 307.4605687464168, (45, 24668): 303.0396975820161, (45, 24711): 311.043616684584, (45, 24756): 313.07158972361964, (45, 24788): 313.3059839084606, (45, 24809): 311.92846758943074, (45, 24813): 312.2932609802905, (45, 24821): 312.1434453606194, (45, 24825): 312.3840646022745, (45, 24832): 311.73166442674574, (45, 24833): 312.0163358858197, (45, 24835): 312.3392814580409, (45, 24837): 312.69997709171497, (45, 24840): 311.7351275338705, (45, 24841): 312.076526314583, (45, 24844): 311.8125097516285, (45, 24845): 311.82013987481764, (45, 24846): 312.14976729228897, (45, 24849): 312.3358720962571, (45, 24850): 312.45886411115146, (45, 24863): 308.03782413300365, (45, 24866): 308.52176354130427, (45, 24885): 309.3386000822812, (45, 24886): 309.52248630956956, (45, 24889): 310.12974530799386, (45, 24903): 310.33743703270324, (45, 24909): 308.1507503018839, (45, 24999): 328.36866765616435, (45, 25019): 327.22973915192813, (45, 25028): 328.19647480223233, (45, 25137): 300.58115032687385, (45, 25145): 301.3370836342205, (45, 25208): 312.00635827215774, (45, 25233): 311.03243832647166, (45, 25371): 299.30398393818825, (45, 25377): 296.7194347607902, (45, 25828): 256.4722844974216, (45, 25851): 249.3188880731014, (45, 25874): 255.40388136124926, (45, 25898): 259.0889283661705, (45, 25946): 255.78799138172056, (45, 26047): 270.4900078428436, (45, 26066): 279.8152577032563, (45, 26197): 272.9896422915619, (45, 26212): 241.32415234573944, (45, 26253): 239.8585763924198, (45, 26254): 240.28631175578957, (45, 26257): 241.21510333070393, (45, 26258): 240.27330359787967, (45, 26260): 240.7262359724951, (45, 26266): 239.2128439882802, (45, 26267): 239.89845326992477, (45, 26271): 240.03470735106134, (45, 26304): 244.87473087627805, (45, 26305): 244.5287376360921, (45, 26363): 255.88229368730242, (45, 26441): 210.0055083850095, (45, 26442): 209.77477164042665, (45, 26450): 210.3423359474149, (45, 26459): 211.76596145348293, (45, 26462): 212.30045383487297, (45, 26467): 210.93085716427825, (45, 26471): 210.60364481295753, (45, 26472): 210.43784471301475, (45, 26473): 210.2540736226163, (45, 26476): 208.42696603432407, (45, 26485): 210.83809030245166, (45, 26493): 210.1107455257005, (45, 26524): 212.71122410093724, (45, 26525): 212.3859133409335, (45, 26556): 210.85729011219686, (45, 26560): 212.06726207863343, (45, 26561): 212.631968275509, (45, 26564): 210.66744162789675, (45, 26569): 212.3210074858398, (45, 26570): 211.9976347547857, (45, 26573): 211.30252177550292, (45, 26581): 210.76368177936467, (45, 26583): 211.20929409794084, (45, 26593): 210.06472733002892, (45, 26837): 210.27233004907023, (45, 26844): 210.22547027172297, (45, 26863): 208.97720886784606, (45, 26893): 208.26079791277363, (45, 26902): 208.1467806949989, (45, 26905): 209.48582130004635, (45, 26912): 209.01109129868436, (45, 26921): 208.71548308669847, (45, 26922): 207.05781092520922, (45, 27212): 237.6279972127586, (45, 27218): 238.8901421232199, (45, 27239): 237.28437071799283, (45, 27257): 236.90167047977712, (45, 27274): 237.02546106162666, (45, 27279): 236.56174460080564, (45, 27282): 236.6417689979834, (45, 27283): 237.52321400823828, (45, 27285): 236.70863779850745, (45, 27286): 235.95767923098632, (45, 27290): 236.63547596995338, (45, 27295): 237.38572268755647, (45, 27300): 237.19849739089042, (45, 27344): 235.29813072142787, (45, 27366): 234.73845794218107, (45, 27383): 235.7121952989145, (45, 27398): 236.77442053342114, (45, 27406): 237.19098871746482, (45, 27407): 237.54805860564596, (45, 27426): 240.82660989814886, (45, 27432): 240.1592829722929, (45, 27460): 240.9986258211622, (45, 27523): 227.35538841671058, (45, 27545): 234.61506728754767, (45, 27602): 230.5991699598795, (45, 27606): 231.21557428643368, (45, 27646): 223.18865506781177, (45, 27667): 222.41913943629334, (45, 27672): 222.75452444290488, (45, 27674): 222.64903183580532, (45, 27688): 224.01754256479416, (45, 27692): 222.19803361996549, (45, 27693): 222.23061223732526, (45, 27705): 221.8104977544916, (45, 27712): 221.4337643046265, (45, 27786): 245.95142881857268, (45, 27790): 251.123248046828, (45, 27791): 251.86773381719874, (45, 27795): 245.49173745717948, (45, 27801): 248.87660192343526, (45, 27813): 245.3568887508669, (45, 27816): 246.39466997844818, (45, 27823): 249.05089908012332, (45, 27830): 247.5869476236871, (45, 27884): 220.37208765506944, (45, 27885): 222.87286120538207, (45, 27896): 221.55825018217706, (45, 27919): 221.8656018457248, (45, 27922): 221.5817329252407, (45, 27930): 221.2523002464147, (45, 27934): 220.98926122255068, (45, 27935): 220.65027776716693, (45, 27948): 210.76584047027163, (45, 27951): 217.232877661854, (45, 28061): 168.85208909604893, (45, 28290): 167.86067348858708, (45, 28292): 165.95293143902313, (45, 28293): 167.33836314474644, (45, 28295): 166.14350243120373, (45, 28296): 167.21885525634366, (45, 28297): 168.73983325518694, (45, 28302): 167.66294708628834, (45, 28310): 81.76233907957555, (45, 28313): 79.75721703755215, (45, 28372): 82.62660629925901, (45, 28398): 82.34782230192438, (45, 28399): 82.35515785721276, (45, 28400): 81.94506595509732, (45, 28401): 83.40326579375598, (45, 28445): 79.23360545702157, (45, 28475): 86.39513420467193, (45, 28885): 303.78005669563356, (45, 28886): 303.5044630913176, (45, 28915): 304.19934861261356, (45, 28916): 303.7665645447445, (45, 28917): 303.6475713283907, (45, 28921): 304.3853371040504, (45, 28931): 304.38549103111217, (45, 28945): 303.81828032180783, (45, 28982): 303.8490428425857, (45, 29219): 307.96398234774284, (45, 29228): 306.19148496283117, (45, 29246): 318.6598759499042, (45, 29248): 318.8619138215515, (45, 29282): 316.3490901237175, (45, 29290): 319.47541031481666, (45, 29291): 319.0892950981506, (45, 29292): 319.503200446618, (45, 29293): 318.5389303850505, (45, 29294): 319.46043158314217, (45, 29298): 318.7081547246321, (45, 29299): 318.7232637231309, (45, 29304): 317.6068217700549, (45, 29317): 315.1653729966375, (45, 29323): 314.96470057745125, (45, 29330): 316.1579619753456, (45, 29331): 316.66863926356405, (45, 29344): 308.91194536967845, (45, 29445): 290.26494567422986, (45, 29724): 16.40413556403815, (45, 29738): 16.30780779193009, (45, 29745): 17.1967561861794, (45, 29748): 20.124628061744758, (45, 29750): 21.23723927550323, (45, 29759): 19.89835163515622, (45, 29772): 19.592948095275307, (45, 29781): 19.738823215676614, (45, 29784): 18.502237479449224, (45, 29790): 20.208890066219436, (45, 29811): 21.696921902999936, (45, 29817): 29.13628661999207, (45, 29818): 29.301262992069088, (45, 29929): 15.380156083896884, (45, 30039): 12.5, (45, 30066): 12.5, (45, 30116): 16.623923046468434, (45, 30238): 37.84308525645247, (45, 30248): 23.537484091511264, (45, 30260): 23.077552995711493, (45, 30545): 296.596944159925, (45, 30733): 277.28422160215825, (45, 30756): 274.99361980694226, (45, 30921): 282.8553720265987, (45, 31079): 221.82605881515022, (45, 31149): 222.5142532749638, (45, 31154): 222.0806543319014, (45, 31160): 222.45653265491956, (45, 31163): 221.83803253492863, (45, 31189): 216.5350197373515, (45, 31215): 216.39305391950626, (45, 31259): 213.44203935409007, (45, 31262): 212.9940593237651, (45, 31430): 221.05809902725608, (45, 31568): 199.9548047515377, (45, 31751): 217.37252836585048, (47, 109): 242.66761368235396, (47, 872): 78.13798993023534, (47, 873): 77.58148260320027, (47, 877): 77.35977785912739, (47, 879): 77.23523228403702, (47, 884): 76.84381658392006, (47, 889): 76.69166057176888, (47, 891): 77.14643723275378, (47, 892): 76.89446197577682, (47, 894): 77.14086441547417, (47, 896): 78.38934647745597, (47, 903): 76.8487167826998, (47, 909): 79.20873722219909, (47, 910): 79.38130662102567, (47, 912): 79.65818517004988, (47, 913): 79.8220669473743, (47, 916): 80.46850021296078, (47, 926): 79.72280811677389, (47, 927): 79.99756066751561, (47, 948): 77.4219081007501, (47, 961): 78.81081649482721, (47, 962): 79.02530777582794, (47, 963): 79.17745482862601, (47, 967): 76.78696526692194, (47, 974): 76.08743676878234, (47, 998): 76.2129535484981, (47, 1014): 71.66329606450405, (47, 1086): 91.16255632321536, (47, 1087): 92.68366861292577, (47, 1089): 92.37105956441542, (47, 1090): 92.04462466314651, (47, 1092): 91.33973768020313, (47, 1097): 91.5888681175853, (47, 1107): 91.92404001922363, (47, 1387): 198.79070773480237, (47, 1554): 208.2330314720423, (47, 1827): 51.02610699284169, (47, 1828): 51.241491499208976, (47, 1829): 51.071269494287, (47, 1830): 50.02329325135303, (47, 1831): 50.20352981450239, (47, 1832): 50.317679195995694, (47, 1833): 50.49907568330784, (47, 1836): 50.717037507042306, (47, 1841): 50.38269847509614, (47, 1843): 50.40950670208142, (47, 1844): 50.216338227196225, (47, 1845): 50.08988320720201, (47, 1847): 50.74322518774337, (47, 1848): 50.63483295270623, (47, 1849): 49.97467351867619, (47, 1850): 50.09544955473798, (47, 1851): 50.06774297544803, (47, 1852): 49.64051680721612, (47, 1854): 49.92321072418819, (47, 1856): 50.200731435212354, (47, 1857): 50.412011243012365, (47, 1858): 50.310589736875784, (47, 1861): 50.71433457039099, (47, 1866): 49.843075671051956, (47, 1867): 50.736180534377105, (47, 1868): 51.10217206486595, (47, 1870): 49.67700037210854, (47, 1871): 51.095592853298044, (47, 1875): 50.21231559369351, (47, 1880): 50.51660202400458, (47, 1882): 49.88739191495078, (47, 1883): 50.57099156439486, (47, 1889): 51.17658045589428, (47, 1893): 51.756806846916284, (47, 1894): 51.91552509708458, (47, 1899): 51.502196656251606, (47, 1900): 51.615527117842255, (47, 1902): 51.69251634448794, (47, 1905): 51.371046927323825, (47, 1907): 51.01874490366519, (47, 1910): 51.5207594522972, (47, 1917): 52.655862879055526, (47, 1920): 51.38647873111159, (47, 1935): 52.175289715967814, (47, 1937): 51.99971338335288, (47, 1946): 52.55084582146926, (47, 1949): 52.72731953193443, (47, 1950): 51.80315735513483, (47, 1951): 52.01418738591016, (47, 1952): 50.87613144793581, (47, 1953): 51.864102850608575, (47, 1954): 51.15485220020798, (47, 1958): 52.28191796074682, (47, 1960): 51.95254952937873, (47, 1968): 51.82637132037984, (47, 1969): 52.98612432143816, (47, 1974): 52.60597158756896, (47, 1975): 52.33176480333694, (47, 1979): 52.902752251559015, (47, 1980): 52.08490742069503, (47, 1981): 52.59157672801527, (47, 1985): 52.81259739215698, (47, 1994): 49.9602775948213, (47, 2011): 49.608949082094945, (47, 2019): 48.32715955942064, (47, 2020): 48.4832222050454, (47, 2029): 48.299929606397356, (47, 2030): 48.60551267173175, (47, 2032): 47.861215580369546, (47, 2033): 48.35487238483742, (47, 2034): 47.95216108831459, (47, 2036): 46.25544291298428, (47, 2037): 46.75145507835877, (47, 2038): 48.63971366073501, (47, 2042): 48.134194787168404, (47, 2050): 48.96652527451926, (47, 2051): 48.54112273086374, (47, 2053): 48.71592278323154, (47, 2054): 48.64992233212491, (47, 2066): 48.71006202562057, (47, 2067): 48.9319953273555, (47, 2071): 50.30764920573402, (47, 2072): 50.5197929842143, (47, 2073): 51.94533737026119, (47, 2074): 51.685848029243836, (47, 2080): 51.20267423793075, (47, 2082): 50.53972891885132, (47, 2083): 50.68034453618592, (47, 2089): 51.077472289094715, (47, 2090): 51.28040440711712, (47, 2092): 51.574119349085564, (47, 2098): 51.67975299697175, (47, 2099): 51.36175874372663, (47, 2101): 51.312390171265385, (47, 2102): 51.54645030921493, (47, 2103): 51.31280023002116, (47, 2104): 51.00760262888792, (47, 2106): 50.48793359066203, (47, 2112): 50.986507175943245, (47, 2113): 51.349611969390246, (47, 2114): 50.75625667313571, (47, 2117): 50.195873398515396, (47, 2123): 65.07946362454469, (47, 2124): 65.13672083899367, (47, 2134): 63.96505704646585, (47, 2138): 64.53345210593265, (47, 2141): 64.29513239988006, (47, 2148): 60.447675201090135, (47, 2150): 63.98264307045244, (47, 2151): 63.747090620314914, (47, 2152): 63.688607358874734, (47, 2153): 60.840220384298114, (47, 2154): 60.87539407248612, (47, 2155): 60.19056200313331, (47, 2156): 60.62986169527002, (47, 2157): 58.260451310575796, (47, 2160): 62.72232800360186, (47, 2161): 63.29109910822287, (47, 2162): 59.36131111818204, (47, 2163): 59.419036980885515, (47, 2164): 59.17578586166739, (47, 2168): 61.989468459040495, (47, 2172): 60.23613096104899, (47, 2174): 63.247120862583, (47, 2178): 59.74893853202312, (47, 2179): 59.56846671306457, (47, 2183): 64.07474383592825, (47, 2185): 63.835438859687436, (47, 2186): 63.918989290165136, (47, 2190): 63.1635715161949, (47, 2192): 63.227250453759154, (47, 2193): 64.22675411192712, (47, 2194): 64.29312487637924, (47, 2195): 63.78219428710282, (47, 2197): 62.958349164509464, (47, 2205): 62.31673919741014, (47, 2207): 61.657701276241795, (47, 2208): 61.92093910831371, (47, 2212): 65.35060686937258, (47, 2214): 58.1472791947338, (47, 2225): 56.494119894637294, (47, 2231): 67.74741645266175, (47, 2278): 52.474877708160435, (47, 2284): 51.52638203186355, (47, 2285): 51.198956585291334, (47, 2291): 49.17826134445577, (47, 2292): 51.877145992021696, (47, 2307): 51.528470194371494, (47, 2313): 48.36282100758946, (47, 2317): 53.088284641247334, (47, 2319): 51.56041384431461, (47, 2321): 51.0476875766487, (47, 2323): 51.825709748243234, (47, 2326): 53.062482564386805, (47, 2327): 53.109366464791975, (47, 2329): 53.06372496675561, (47, 2330): 52.831820976058374, (47, 2332): 52.385274977764766, (47, 2344): 53.629306464125264, (47, 2346): 53.09353560153587, (47, 2361): 57.61541367427972, (47, 2368): 54.590252458892124, (47, 2374): 54.153791844325184, (47, 2375): 54.41800257666022, (47, 2377): 54.90985017457437, (47, 2378): 54.17474491995775, (47, 2379): 53.62924973330723, (47, 2380): 54.00779576607003, (47, 2383): 55.207290707288905, (47, 2385): 55.37893351875406, (47, 2395): 55.859394419916995, (47, 2397): 53.39361469971654, (47, 2398): 55.017115790896135, (47, 2399): 55.20823785614751, (47, 2400): 55.2325376993851, (47, 2402): 53.62732963467953, (47, 2403): 53.5586051102945, (47, 2404): 53.76389883950513, (47, 2405): 53.732099256357536, (47, 2407): 54.07953308306507, (47, 2408): 53.77111674665991, (47, 2409): 53.82505832505517, (47, 2411): 52.65590280497855, (47, 2412): 53.01227034957622, (47, 2413): 52.83356086125041, (47, 2414): 52.80050866646441, (47, 2422): 52.361275140212435, (47, 2424): 53.19146843414102, (47, 2426): 53.36095445057941, (47, 2433): 53.12789630364589, (47, 2436): 52.5692860322734, (47, 2437): 53.1684077058549, (47, 2440): 53.189962299572855, (47, 2445): 47.299266172010704, (47, 2447): 47.818288300640795, (47, 2454): 47.81992099868737, (47, 2455): 48.24666537135698, (47, 2460): 47.75542662964584, (47, 2461): 47.708610125796845, (47, 2471): 45.61609611747304, (47, 2492): 28.68451298319431, (47, 2511): 31.482313832112087, (47, 2523): 29.926121988457083, (47, 2525): 29.029731754964775, (47, 2535): 37.85043905642223, (47, 2537): 37.59448929109883, (47, 2538): 38.198197696865954, (47, 2539): 36.083989772804316, (47, 2540): 37.91758894013795, (47, 2542): 37.37990723261544, (47, 2559): 43.92330218102933, (47, 2575): 41.23111122094806, (47, 2599): 45.22257179259229, (47, 2600): 43.64466632726824, (47, 2607): 46.16212745373711, (47, 2627): 24.05593626636321, (47, 2647): 22.915943279952497, (47, 2674): 24.975271250180715, (47, 2681): 23.86531964201316, (47, 2683): 24.472649830266256, (47, 2686): 24.863486256535943, (47, 2689): 28.512333685915294, (47, 2690): 28.34732864979938, (47, 2713): 25.03131126888973, (47, 2714): 24.693430503953106, (47, 2715): 24.987192958933115, (47, 2739): 24.874342646749223, (47, 2740): 24.721807317998262, (47, 2741): 24.982005900826685, (47, 2749): 23.953163423581113, (47, 2750): 24.21502606610453, (47, 2752): 24.502957253619126, (47, 2755): 24.627963041018777, (47, 2758): 24.41987982868498, (47, 2759): 24.495263842537923, (47, 2769): 24.34843269116681, (47, 2771): 24.69873148674839, (47, 2779): 23.33133561839303, (47, 2784): 19.552205432298088, (47, 2800): 18.93374679506957, (47, 2802): 23.33896638285752, (47, 2803): 23.437837687727615, (47, 2804): 23.34259909316707, (47, 2805): 22.99114072721441, (47, 2807): 23.162431767306007, (47, 2809): 22.644172642074057, (47, 2812): 21.41039431461425, (47, 2814): 21.441012684912966, (47, 2817): 20.362176101616143, (47, 2819): 23.67565356227273, (47, 2823): 19.949509503573395, (47, 2832): 23.0785342328125, (47, 2836): 21.86007601204078, (47, 2839): 23.353871422464234, (47, 2841): 20.954419446062573, (47, 2843): 21.067338918647593, (47, 2846): 21.38320112125015, (47, 2849): 22.981538976200557, (47, 2852): 22.80688731078933, (47, 2853): 23.053849866647013, (47, 2876): 22.4661161659414, (47, 2877): 23.43426617655709, (47, 2885): 22.754874224354207, (47, 2918): 25.153735779065833, (47, 2921): 25.278368866284797, (47, 2925): 25.669351453809433, (47, 2926): 26.445938194184976, (47, 2930): 23.722133452832136, (47, 2931): 25.118705336023783, (47, 2938): 24.779278170663126, (47, 2940): 27.69648864506877, (47, 2947): 27.007432157098535, (47, 2949): 24.585970874534237, (47, 2950): 24.36749330783364, (47, 2952): 24.172098475462082, (47, 2958): 24.294712730259683, (47, 2959): 24.92096160678794, (47, 2960): 25.174201733668344, (47, 2961): 24.802641825942494, (47, 2963): 23.91696169309589, (47, 2968): 23.808445695207315, (47, 2976): 24.10373219021678, (47, 2981): 17.828144167868768, (47, 2982): 17.274192276642015, (47, 2984): 16.982744519731014, (47, 3003): 16.163757995629265, (47, 3046): 20.50115242467975, (47, 3050): 18.62958749340856, (47, 3051): 18.96042477328757, (47, 3053): 18.389303595490418, (47, 3069): 19.627348398834837, (47, 3071): 19.604449560926916, (47, 3080): 22.517484800201327, (47, 3199): 13.272787586211756, (47, 3200): 12.5550918985309, (47, 3205): 16.03220760285764, (47, 3209): 12.804957907331527, (47, 3215): 12.741784236853633, (47, 3217): 12.5, (47, 3249): 12.977182735389158, (47, 3263): 18.30584950352909, (47, 3289): 15.105066838858827, (47, 3301): 14.829170719062446, (47, 3302): 14.735718460287199, (47, 3307): 14.474094516030975, (47, 3310): 15.12790324669525, (47, 3391): 20.05897306304706, (47, 3509): 103.06009482217833, (47, 3510): 103.56396227281799, (47, 3511): 103.30974539308714, (47, 3512): 103.69400545336669, (47, 3514): 103.65574664395827, (47, 3519): 101.50742996704544, (47, 3536): 102.31778068606603, (47, 3545): 101.61677815010017, (47, 3548): 102.50313524759524, (47, 3572): 101.93022780340102, (47, 3581): 102.27886590438027, (47, 3583): 102.94749381330156, (47, 3601): 100.45043440090693, (47, 3656): 101.0322449126923, (47, 3669): 101.6234210855386, (47, 3670): 101.15254459068993, (47, 3695): 103.90887048090397, (47, 3696): 103.55468685818975, (47, 3782): 104.22434923017619, (47, 3792): 104.43275920362429, (47, 3989): 315.61151890650694, (47, 4008): 318.0752299761763, (47, 4031): 317.4100407292112, (47, 4045): 317.0170947320401, (47, 4144): 317.61922211136704, (47, 4145): 315.6421519823489, (47, 4164): 316.78510405115253, (47, 4168): 316.2493849749083, (47, 4173): 316.20831235910794, (47, 4181): 314.70020208288304, (47, 4228): 312.7496121757803, (47, 4248): 312.83952422450767, (47, 4254): 301.2941107359803, (47, 4260): 301.1418610701303, (47, 4262): 302.15085738071303, (47, 4273): 301.82960561628045, (47, 4319): 294.507993071184, (47, 4326): 294.19179915196275, (47, 4328): 294.25103730507817, (47, 4334): 294.90959450696056, (47, 4335): 294.74267264377, (47, 4372): 289.7536876318803, (47, 4413): 297.8217593865703, (47, 4434): 289.4818503344263, (47, 4447): 290.8147704730788, (47, 4452): 289.5611311708089, (47, 4463): 270.83712209444207, (47, 4465): 271.5220025816288, (47, 4619): 297.94273510058406, (47, 4645): 300.00212847247803, (47, 4657): 299.58516916669964, (47, 4666): 298.73573968034844, (47, 4676): 300.0813184362427, (47, 4678): 300.4361725838677, (47, 4689): 299.38158854717324, (47, 4704): 306.0405003912546, (47, 4726): 319.3103140141183, (47, 4727): 319.05397860344993, (47, 4730): 318.5675832707676, (47, 4731): 318.6359306314, (47, 4734): 319.3222094900621, (47, 4735): 319.0182008330051, (47, 4736): 319.0879216444098, (47, 4737): 318.5845034584012, (47, 4738): 318.59923523061354, (47, 4756): 318.8231205420343, (47, 4760): 317.834000299189, (47, 4761): 318.09879128294585, (47, 4762): 317.41026123859257, (47, 4765): 317.92467757487964, (47, 4773): 319.87489459670513, (47, 4774): 319.5393926065079, (47, 4790): 319.7204812199253, (47, 4795): 319.5231582699926, (47, 4799): 319.5936243060637, (47, 4801): 319.983766906548, (47, 4804): 319.7434310961859, (47, 4805): 319.5795814089655, (47, 4806): 319.2843682896495, (47, 4815): 318.94450539982466, (47, 4816): 319.63525337183563, (47, 4817): 319.638512612779, (47, 4826): 319.29433472313127, (47, 4830): 318.87754156962103, (47, 4839): 318.5759879016642, (47, 4840): 318.75322910449927, (47, 4841): 318.17013623010183, (47, 4846): 318.0126197285978, (47, 4848): 317.84989757193915, (47, 4850): 318.0653135720395, (47, 4871): 315.55962277158045, (47, 4883): 317.6958126678999, (47, 4900): 316.7421922425516, (47, 4901): 316.340312254838, (47, 4917): 295.84505739397974, (47, 4931): 293.844411460185, (47, 4944): 296.150925499257, (47, 4956): 294.13238816365345, (47, 4958): 293.9180917538516, (47, 4959): 293.4309835887704, (47, 4961): 294.6013101694743, (47, 4966): 293.55286342851196, (47, 5207): 291.3198796299984, (47, 5272): 257.6164514279338, (47, 5283): 258.3086340640738, (47, 5287): 259.10138803285423, (47, 5289): 259.39285142345284, (47, 5293): 258.04507755578675, (47, 5295): 260.02762805494507, (47, 5296): 259.8248437843254, (47, 5298): 259.69581239492027, (47, 5303): 260.11808844268603, (47, 5305): 256.8403136079487, (47, 5306): 256.02182799863425, (47, 5307): 256.4579937201874, (47, 5308): 257.1028079442159, (47, 5313): 257.31228278116083, (47, 5314): 257.8290624173427, (47, 5317): 256.9828842684622, (47, 5319): 259.39065274791943, (47, 5324): 259.1365117576511, (47, 5326): 258.98371541316953, (47, 5348): 255.6936921348524, (47, 5351): 255.94627090614748, (47, 5399): 259.51235585197566, (47, 5413): 256.4164000709685, (47, 5422): 260.0850263007006, (47, 5445): 258.38283289546064, (47, 5448): 257.7058132868956, (47, 5456): 257.34395382164445, (47, 5467): 257.9188210337631, (47, 5624): 251.12055039067266, (47, 5671): 275.691108330786, (47, 5672): 274.7813609261544, (47, 5797): 286.6626823924012, (47, 5871): 267.18148237439686, (47, 5976): 259.11097010956314, (47, 6118): 44.230973856207505, (47, 6248): 43.14472697102974, (47, 6345): 215.90788740479863, (47, 6352): 213.49145488079606, (47, 6354): 216.50338859179618, (47, 6359): 216.97302629471363, (47, 6376): 213.86246783314428, (47, 6378): 216.21574818336524, (47, 6381): 216.7703912953297, (47, 6383): 215.39807890889958, (47, 6396): 216.47938669702336, (47, 6399): 215.9302900756241, (47, 6408): 213.58525957691268, (47, 6409): 214.74720778065475, (47, 6419): 210.88617454166993, (47, 6422): 213.92015082315476, (47, 6423): 213.7262846851299, (47, 6424): 216.29705447380644, (47, 6439): 215.84333959769478, (47, 6464): 215.1835216729693, (47, 6465): 214.9294796629526, (47, 6469): 215.20925465541856, (47, 6470): 215.05650796711987, (47, 6472): 217.78924154630056, (47, 6480): 217.33584573846133, (47, 6486): 218.86494759127277, (47, 6497): 218.35242505394797, (47, 6503): 215.44841486709498, (47, 6508): 215.55717418183494, (47, 6509): 216.0548440078313, (47, 6521): 217.6713041292318, (47, 6544): 217.56227476133955, (47, 6552): 214.4065893159193, (47, 6553): 214.03499699989777, (47, 6554): 213.656195272371, (47, 6578): 215.01987873301786, (47, 6582): 214.80365391569532, (47, 6601): 215.2021332353073, (47, 6609): 218.1495437627646, (47, 6610): 218.26707884485972, (47, 6611): 218.31348599822604, (47, 6614): 218.1032065298507, (47, 6615): 218.18109681186417, (47, 6616): 218.60781333554365, (47, 6617): 218.42313738316452, (47, 6618): 219.01558308923921, (47, 6619): 217.83580623026742, (47, 6620): 218.63481669259917, (47, 6621): 218.31959759297922, (47, 6622): 218.38093925510555, (47, 6623): 218.08634370430673, (47, 6624): 217.81987193652978, (47, 6625): 217.75053647261598, (47, 6626): 217.81122882591956, (47, 6627): 218.011659313927, (47, 6628): 218.5890532274066, (47, 6629): 217.93116654445492, (47, 6630): 217.4498286543755, (47, 6632): 217.8880216109082, (47, 6634): 217.11461180443888, (47, 6635): 218.19433595360917, (47, 6636): 218.6322028896971, (47, 6637): 217.4946237103591, (47, 6638): 217.50394703768634, (47, 6639): 218.05325971310796, (47, 6640): 217.5495745269092, (47, 6641): 218.32716954915918, (47, 6642): 217.52251806609587, (47, 6643): 217.76448713543718, (47, 6645): 217.88775851336024, (47, 6646): 218.8853512250381, (47, 6647): 217.61257332253373, (47, 6653): 218.1617729116965, (47, 6655): 218.0520969375447, (47, 6658): 217.09721763449147, (47, 6662): 217.516606655407, (47, 6819): 199.566975466396, (47, 6996): 206.40773574211923, (47, 7059): 210.66041005308304, (47, 7187): 205.71189596630947, (47, 7304): 195.16551733894605, (47, 7528): 206.91567586987824, (47, 7720): 231.4547234007488, (47, 7793): 231.25972117748816, (47, 7807): 231.49762935627965, (47, 7808): 231.21300708103857, (47, 7831): 220.63013906359964, (47, 7850): 224.57187621479858, (47, 7852): 223.61082854612482, (47, 8012): 229.840575756031, (47, 8125): 235.81487442271722, (47, 8208): 239.32162568649153, (47, 8392): 224.31035115032495, (47, 8651): 179.1053200524126, (47, 9088): 197.71204124105054, (47, 9443): 172.74470166239257, (47, 9444): 173.4211922384544, (47, 9828): 157.13722374938195, (47, 9868): 153.93145993594055, (47, 10180): 236.4046903792694, (47, 10256): 247.45713819975018, (47, 10276): 242.05715899479782, (47, 10378): 242.4951444978588, (47, 10676): 234.39610014053915, (47, 10714): 227.73264962435718, (47, 10730): 227.74687967512867, (47, 10862): 232.73449429585665, (47, 10881): 234.44194264723663, (47, 10883): 234.23161078784815, (47, 10885): 232.37268365607613, (47, 10891): 233.90709487594262, (47, 10909): 233.80722417339513, (47, 10911): 234.0983489756199, (47, 10913): 233.68758993249193, (47, 10915): 233.69651990311937, (47, 10919): 233.95655258805235, (47, 11037): 221.89419765281087, (47, 11039): 217.76006763048525, (47, 11516): 336.6498780406317, (47, 11856): 295.1712647418518, (47, 11857): 294.93839527672384, (47, 11861): 295.0732800229527, (47, 11881): 294.4108131123239, (47, 11902): 292.5530139525465, (47, 11911): 292.0558487258972, (47, 11914): 292.38432090287574, (47, 11922): 293.82059094255317, (47, 11924): 294.21717484018757, (47, 11926): 293.6725422000918, (47, 11950): 294.550174099918, (47, 11963): 296.3239123742198, (47, 11983): 294.8262580540942, (47, 11985): 297.2289351523684, (47, 12009): 296.6227544075453, (47, 12010): 295.43066782993907, (47, 12018): 295.6020399054789, (47, 12020): 295.9811506672358, (47, 12021): 296.1601651412286, (47, 12024): 297.36036123249, (47, 12025): 297.00847978973184, (47, 12027): 296.71099830981694, (47, 12031): 295.2221444117167, (47, 12032): 295.6813817096314, (47, 12035): 296.48152992583243, (47, 12041): 297.5312546069213, (47, 12045): 280.6007202755339, (47, 12145): 287.99839594879836, (47, 12275): 315.703897921205, (47, 12294): 312.1057726027857, (47, 12358): 321.66918206157976, (47, 12463): 325.1304057316052, (47, 12465): 324.9931460131219, (47, 12482): 327.0157050832881, (47, 12503): 326.69770044680587, (47, 12506): 327.16645882947125, (47, 12549): 326.53895679511584, (47, 12559): 326.1042561666927, (47, 12569): 326.35135441714215, (47, 12572): 326.7117795799052, (47, 12574): 326.00129241296673, (47, 12576): 326.99309273841016, (47, 12591): 327.1295810068211, (47, 12608): 330.1467172295029, (47, 12696): 325.7152354788055, (47, 12710): 328.6801677218464, (47, 12728): 327.0650422475003, (47, 12766): 251.4120484377143, (47, 12771): 248.80055677199593, (47, 12790): 248.32317545863026, (47, 12795): 247.1322370163699, (47, 12797): 243.30130358986165, (47, 12798): 243.91811556252514, (47, 12811): 247.2866205406723, (47, 12830): 246.01370151288822, (47, 12848): 246.89293990492942, (47, 12850): 247.35290155942965, (47, 12852): 245.94003171335024, (47, 12854): 245.42027726161726, (47, 12859): 247.4866099011822, (47, 12861): 244.55823725552074, (47, 12865): 247.79752398772885, (47, 12866): 247.61500058829114, (47, 12867): 248.5802989533358, (47, 12874): 248.10012840319894, (47, 12875): 248.53004398025493, (47, 12881): 246.81885871971568, (47, 12883): 247.47200186352615, (47, 12885): 248.85231774030254, (47, 12888): 247.22974985229882, (47, 12889): 247.139961223512, (47, 12892): 248.17914664021887, (47, 12893): 247.1951276349793, (47, 12896): 247.56440756171375, (47, 12906): 247.87829119163274, (47, 13018): 241.75657972601348, (47, 13071): 241.51171198194635, (47, 13131): 238.52010384288258, (47, 13146): 242.24282964363502, (47, 13159): 235.89266289649152, (47, 13193): 237.93942249842553, (47, 13198): 232.39025568070667, (47, 13292): 239.5237653356533, (47, 13296): 242.0881694236382, (47, 13406): 227.7404046902395, (47, 13407): 227.47513045153715, (47, 13417): 226.51053283850283, (47, 13418): 227.09111500571078, (47, 13438): 230.16032133390482, (47, 13442): 230.8605946544964, (47, 13443): 230.3232115789727, (47, 13764): 182.47010388839985, (47, 13766): 183.15046276214844, (47, 13771): 182.4227213024724, (47, 13783): 182.02001359747803, (47, 13784): 183.92155402431075, (47, 13792): 181.025463303738, (47, 13824): 181.53813421349972, (47, 14017): 186.0653661098995, (47, 14870): 233.78096304600734, (47, 14997): 202.83261420805917, (47, 15000): 203.0769836436063, (47, 15003): 203.70880302315263, (47, 15006): 203.9405497859829, (47, 15007): 204.41547689358387, (47, 15056): 204.8833304360854, (47, 15063): 204.58083489277436, (47, 15069): 204.63438252951076, (47, 15076): 204.6107561244484, (47, 15086): 202.95406481794376, (47, 15087): 202.70329398567563, (47, 15111): 201.1575319984196, (47, 15116): 202.06260028108645, (47, 15722): 189.82142048406723, (47, 15998): 186.76810951124506, (47, 16073): 92.74817335617936, (47, 16939): 45.79332299553745, (47, 16940): 46.3243376258946, (47, 16951): 44.49112488943166, (47, 16963): 44.742112134192055, (47, 16965): 44.64083098961331, (47, 16969): 44.01925429017265, (47, 16970): 44.94313035347611, (47, 16971): 45.08569521212338, (47, 16973): 44.657355206039924, (47, 16974): 44.174793676658965, (47, 16976): 45.21483684862086, (47, 16978): 45.4697203242231, (47, 16980): 45.549240933827974, (47, 16982): 43.709122187209296, (47, 17045): 12.5, (47, 17048): 12.5, (47, 17304): 309.8216137589638, (47, 17305): 309.1001391640913, (47, 17330): 309.61237944907833, (47, 17334): 308.9954198534003, (47, 17343): 310.21326188119326, (47, 17345): 308.6779223531944, (47, 17347): 309.3649716052763, (47, 17351): 307.80765484035845, (47, 17372): 308.79012806952, (47, 17373): 310.2055399990029, (47, 17377): 310.2814795512861, (47, 17382): 309.2994616683267, (47, 17383): 309.57776244855967, (47, 17389): 308.9749403833658, (47, 17400): 310.0216529218827, (47, 17401): 310.04731009893436, (47, 17402): 310.05222575027454, (47, 17403): 310.12701282203744, (47, 17440): 308.42660873441014, (47, 17455): 309.852054114819, (47, 17491): 309.73278649190274, (47, 17507): 309.05612172499235, (47, 17509): 309.68572274274163, (47, 17590): 307.11585418994514, (47, 17615): 305.8175604182753, (47, 17642): 306.23993537968454, (47, 17643): 306.08464539717437, (47, 17668): 305.8614315316212, (47, 17721): 305.1339656694563, (47, 17754): 310.5992466018782, (47, 17769): 309.56012523362756, (47, 17776): 306.8182126296892, (47, 17804): 310.52134966239674, (47, 17809): 311.086013314272, (47, 17824): 310.8941314798131, (47, 17837): 308.42603375460726, (47, 17838): 308.3267767727559, (47, 17862): 307.8305629224066, (47, 17866): 309.10705031945105, (47, 17872): 307.52348496733885, (47, 17873): 306.5122435841737, (47, 17881): 308.0399334386503, (47, 17947): 101.66959000032669, (47, 17951): 102.05544954631469, (47, 17953): 102.44551861849737, (47, 17954): 102.62424950933219, (47, 17959): 101.20133639863244, (47, 17963): 100.79557829340887, (47, 18000): 103.9644976744851, (47, 18001): 104.24659676129343, (47, 18111): 114.16723674262488, (47, 18148): 126.93328551731949, (47, 18166): 122.9201619580685, (47, 18189): 116.30048350170102, (47, 18239): 310.6000701107717, (47, 18240): 310.55785448862446, (47, 18245): 310.6343823034145, (47, 18247): 310.47323607359294, (47, 18251): 310.589022618568, (47, 18256): 310.6730897955626, (47, 18258): 310.5111358322021, (47, 18259): 310.5174231532845, (47, 18260): 310.54547784125873, (47, 18262): 310.6250529265649, (47, 18263): 310.6899067015048, (47, 18264): 310.72009686778995, (47, 18266): 310.6351959294243, (47, 18267): 310.6697294354738, (47, 18268): 310.67336152626814, (47, 18269): 310.73834434739075, (47, 18275): 310.70752818307784, (47, 18285): 310.7238834851573, (47, 18308): 310.03455630549354, (47, 18313): 309.70067224056027, (47, 18314): 309.742880856367, (47, 18315): 310.8338238440109, (47, 18316): 310.77939460416235, (47, 18317): 310.80678067695277, (47, 18320): 310.90191239819774, (47, 18321): 310.89536249923594, (47, 18322): 310.94825241829284, (47, 18324): 311.0596735372144, (47, 18325): 311.29073724840487, (47, 18326): 311.2068527198216, (47, 18327): 310.7917745268623, (47, 18329): 311.4479706075948, (47, 18330): 311.18346523398486, (47, 18331): 311.05240992424046, (47, 18332): 310.8926747290744, (47, 18333): 311.2019987034586, (47, 18336): 311.1439196206733, (47, 18337): 311.25295171150606, (47, 18403): 310.8666353407063, (47, 18432): 306.3128529728775, (47, 18451): 309.3930765077007, (47, 18466): 312.5154508054283, (47, 18481): 311.020169112266, (47, 18483): 310.98659676319954, (47, 18484): 310.88508176850144, (47, 18485): 310.6130415710921, (47, 18486): 311.0725802070756, (47, 18487): 310.81669633661653, (47, 18489): 310.9245888350759, (47, 18490): 311.31003563837766, (47, 18491): 311.44943690059085, (47, 18492): 310.4911328309095, (47, 18493): 311.0624982828211, (47, 18494): 310.8410493718152, (47, 18495): 311.21112809318174, (47, 18496): 311.03782074747187, (47, 18497): 310.788278664008, (47, 18498): 310.72173198235754, (47, 18499): 310.9263629153887, (47, 18501): 310.83671617858175, (47, 18502): 310.7095454032645, (47, 18503): 310.5717378249008, (47, 18504): 311.05462689262936, (47, 18506): 310.95112763911516, (47, 18507): 310.8485188857023, (47, 18508): 310.929975589775, (47, 18509): 310.9639592695417, (47, 18510): 310.62122497824777, (47, 18511): 311.16933482919364, (47, 18512): 310.9517177828628, (47, 18515): 311.11408871817434, (47, 18516): 311.23299698537227, (47, 18517): 311.11944020815395, (47, 18518): 311.31249266404353, (47, 18519): 311.06391196231914, (47, 18520): 310.85164440707376, (47, 18522): 311.5594468173435, (47, 18523): 311.6249378823673, (47, 18532): 311.86269742610665, (47, 18535): 311.4058408402466, (47, 18537): 311.1514960349588, (47, 18539): 311.22350671946396, (47, 18540): 311.273003942377, (47, 18541): 311.4146288781824, (47, 18542): 311.5011186307975, (47, 18543): 311.08616886571065, (47, 18546): 311.3442882227561, (47, 18555): 311.74631957925004, (47, 18556): 311.8438704912171, (47, 18565): 311.88146509098027, (47, 18567): 312.06918482881946, (47, 18568): 311.81994840205584, (47, 18577): 313.37712552448636, (47, 18583): 313.0175165405953, (47, 18605): 313.22660710345383, (47, 18608): 312.3457715844751, (47, 18616): 314.68793142841525, (47, 18618): 315.99395262690837, (47, 18625): 315.3080419789752, (47, 18645): 314.1029826858319, (47, 18646): 314.4755462878406, (47, 18653): 313.68895106956523, (47, 18654): 314.6987495796872, (47, 18655): 314.0884781514993, (47, 18666): 317.6864577542852, (47, 18837): 309.3134161282587, (47, 18974): 308.53279656643736, (47, 18999): 309.12541555464765, (47, 19000): 309.490060039795, (47, 19174): 289.9091713040442, (47, 19342): 296.6123885394164, (47, 19455): 294.2414558184712, (47, 19555): 275.37580412834774, (47, 19564): 275.7075269466497, (47, 19573): 275.09343526687456, (47, 19586): 274.8672719426818, (47, 19605): 275.2738060052254, (47, 19611): 275.71703151913096, (47, 19614): 275.7160522145152, (47, 19641): 284.03389059758575, (47, 19702): 283.6577884963173, (47, 19713): 283.09615653885425, (47, 19731): 273.502907424889, (47, 19819): 291.01475608736087, (47, 19893): 279.48834643931247, (47, 19899): 283.6980359974619, (47, 19929): 280.56179808002065, (47, 19951): 288.82850176497186, (47, 19962): 281.2988022177754, (47, 19970): 282.99193136668293, (47, 19971): 283.0591445735918, (47, 19972): 282.38324481950855, (47, 19975): 282.0349033832375, (47, 19978): 290.47432347072964, (47, 19987): 290.6019795899469, (47, 19989): 288.3240142256974, (47, 20039): 291.0139406859726, (47, 20043): 291.9463731438129, (47, 20047): 291.2001548179341, (47, 20052): 288.6953180669508, (47, 20054): 288.90357622842043, (47, 20085): 300.21017166452117, (47, 20104): 300.9207060785909, (47, 20132): 296.5878256023727, (47, 20203): 279.2641472962628, (47, 20280): 278.38710423099553, (47, 20285): 278.17213833194955, (47, 20290): 278.7749227397739, (47, 20297): 277.9996032871446, (47, 20309): 291.19003122222676, (47, 20453): 302.912830910781, (47, 20485): 273.12420353894464, (47, 20520): 271.15366783809634, (47, 20526): 270.47865099795985, (47, 20698): 163.19968509121063, (47, 20868): 139.99645428938604, (47, 21042): 250.83435785305875, (47, 21057): 255.41835856362704, (47, 21066): 253.32619708568356, (47, 21075): 252.23995961725794, (47, 21093): 251.396685944731, (47, 21098): 254.9691193546065, (47, 21127): 251.32721803269723, (47, 21130): 252.29906097906755, (47, 21144): 251.9642108673165, (47, 21146): 251.0263473152102, (47, 21147): 251.82622989182877, (47, 21148): 252.69512053571984, (47, 21153): 249.99753418688812, (47, 21293): 258.7208243404895, (47, 21426): 255.5980450369598, (47, 21442): 260.13727761151284, (47, 21451): 260.58425892805934, (47, 21466): 257.9584218976181, (47, 21469): 258.72699685284493, (47, 21471): 257.5643896282756, (47, 21473): 258.2235732522449, (47, 21475): 257.66029862302713, (47, 21482): 259.1329958351906, (47, 21484): 259.01487602258027, (47, 21488): 258.5425731075134, (47, 21494): 257.76612365892987, (47, 21498): 258.3106636487864, (47, 21500): 257.5361461690383, (47, 21514): 259.4421671314343, (47, 21537): 257.62348966973104, (47, 21662): 260.39696423600515, (47, 21691): 257.47895807301603, (47, 21757): 251.4491635015915, (47, 21777): 242.64718135105204, (47, 21778): 241.91446315291358, (47, 21779): 242.42416767946042, (47, 21790): 243.36381814999646, (47, 21802): 243.5211263818476, (47, 21824): 244.38192930256622, (47, 21874): 242.7374988533942, (47, 21879): 242.49029736890174, (47, 21983): 244.5699797191917, (47, 22002): 253.14462100461893, (47, 22132): 245.8686593185033, (47, 22261): 160.6208206554961, (47, 22298): 162.73190982001452, (47, 22339): 158.47586956415472, (47, 22508): 172.31268678640689, (47, 22841): 57.31834359338934, (47, 22842): 56.94838500931243, (47, 22874): 55.1740291679969, (47, 22941): 56.49225323254191, (47, 22956): 56.47151592194315, (47, 22960): 57.454847121273936, (47, 22968): 52.7187318609759, (47, 22970): 53.54142767732905, (47, 22974): 50.55468548759401, (47, 22980): 50.98498209670488, (47, 23025): 46.441322974233834, (47, 23028): 45.409700132393866, (47, 23081): 40.84407756307719, (47, 23104): 32.44914056041566, (47, 23147): 42.13833616080276, (47, 23298): 272.7713297037536, (47, 23376): 270.7085811049013, (47, 23381): 269.963736220514, (47, 23529): 274.4883419945212, (47, 23556): 273.2326637093436, (47, 23718): 271.0960782302387, (47, 24001): 284.8901082537565, (47, 24094): 289.5598448059873, (47, 24129): 291.61258172976386, (47, 24174): 287.6914365978406, (47, 24235): 292.4800148779759, (47, 24259): 294.2159666678947, (47, 24260): 294.1034347876239, (47, 24261): 293.63001174195955, (47, 24305): 296.46470650552664, (47, 24306): 296.9082164219017, (47, 24307): 296.28267244282773, (47, 24308): 289.4104566368786, (47, 24498): 300.9463375953573, (47, 24499): 301.0084132223272, (47, 24500): 300.6100568889421, (47, 24668): 297.1107189712928, (47, 24711): 303.92261445544193, (47, 24756): 305.6560186251487, (47, 24788): 306.09649163254454, (47, 24809): 304.16606114558886, (47, 24813): 304.7367821492009, (47, 24821): 304.53448915296667, (47, 24825): 304.7485443536827, (47, 24832): 303.9840264425735, (47, 24833): 304.3155197047702, (47, 24835): 304.6652296974528, (47, 24837): 305.14678184441516, (47, 24840): 303.956321508952, (47, 24841): 304.419577329117, (47, 24844): 304.00343711018616, (47, 24845): 304.1802234064659, (47, 24846): 304.3277114503797, (47, 24849): 304.5237697960157, (47, 24850): 304.87716096746306, (47, 24863): 300.03590275937285, (47, 24866): 300.61630323517323, (47, 24885): 301.4254513225804, (47, 24886): 301.54649221441144, (47, 24889): 302.59120322803705, (47, 24903): 302.9810766603585, (47, 24909): 300.65397217731015, (47, 24999): 325.26269728696184, (47, 25019): 324.28878020678474, (47, 25028): 324.98395359234996, (47, 25137): 280.2279187584259, (47, 25145): 281.0423932094388, (47, 25208): 290.6979109972631, (47, 25233): 289.6002778790222, (47, 25371): 280.066777573698, (47, 25377): 277.67223032653095, (47, 25828): 235.69256076027048, (47, 25851): 229.01101825321868, (47, 25874): 235.15623832953457, (47, 25898): 238.20290319389304, (47, 25946): 235.02303578682628, (47, 26047): 248.9222271619975, (47, 26066): 262.5085868976173, (47, 26197): 253.51469942794773, (47, 26212): 216.6953397206081, (47, 26253): 214.8272235409198, (47, 26254): 215.4687868098282, (47, 26257): 216.34598482844822, (47, 26258): 215.26734870569106, (47, 26260): 215.80508976853756, (47, 26266): 214.57887098095955, (47, 26267): 215.29620607792708, (47, 26271): 215.38133342310988, (47, 26304): 221.8098830130651, (47, 26305): 221.59512885723294, (47, 26363): 234.0497326395632, (47, 26441): 175.2130290832724, (47, 26442): 175.06783782330953, (47, 26450): 175.87418299963625, (47, 26459): 177.17132604771564, (47, 26462): 177.60978135561632, (47, 26467): 175.51631526218608, (47, 26471): 175.46285106068467, (47, 26472): 175.33950058664468, (47, 26473): 175.1843968510873, (47, 26476): 173.6894115232051, (47, 26485): 176.19217438564388, (47, 26493): 175.5324941717663, (47, 26524): 177.85012619396167, (47, 26525): 177.5910539288413, (47, 26556): 175.80778976768985, (47, 26560): 176.92569831439948, (47, 26561): 177.6199959529445, (47, 26564): 175.7171483365171, (47, 26569): 177.38484977841946, (47, 26570): 177.16786307363458, (47, 26573): 176.49549473858067, (47, 26581): 176.01847361832893, (47, 26583): 176.48327570602711, (47, 26593): 175.38989940060947, (47, 26837): 174.86377846936273, (47, 26844): 174.62560280256173, (47, 26863): 173.931830174602, (47, 26893): 172.71613497973576, (47, 26902): 172.34506289113838, (47, 26905): 173.8235884281748, (47, 26912): 173.18702647770823, (47, 26921): 173.42244173767588, (47, 26922): 172.48883605006876, (47, 27212): 199.2925918346327, (47, 27218): 200.70325460800254, (47, 27239): 198.65486185383162, (47, 27257): 198.44471321608117, (47, 27274): 198.34280790278592, (47, 27279): 197.92926247371153, (47, 27282): 198.18707782641192, (47, 27283): 198.96628443495717, (47, 27285): 197.9554659454957, (47, 27286): 197.39637211982813, (47, 27290): 198.33594783658677, (47, 27295): 199.17046248013318, (47, 27300): 198.4789669656172, (47, 27344): 197.13359541727172, (47, 27366): 196.3885533825655, (47, 27383): 196.97817929371186, (47, 27398): 197.7847212178088, (47, 27406): 198.3654101078294, (47, 27407): 198.65791405415555, (47, 27426): 202.06783774132597, (47, 27432): 202.1921726803274, (47, 27460): 202.52053432113678, (47, 27523): 189.27206570584795, (47, 27545): 193.0795020213789, (47, 27602): 185.41889482982177, (47, 27606): 185.9665953636235, (47, 27646): 182.08785648932667, (47, 27667): 180.52689619867832, (47, 27672): 180.80896180078827, (47, 27674): 180.84501274252136, (47, 27688): 182.05479725672637, (47, 27692): 180.13048041989774, (47, 27693): 180.28314924014833, (47, 27705): 179.8832422206667, (47, 27712): 179.45921437124986, (47, 27786): 200.62596187440218, (47, 27790): 206.21512947342725, (47, 27791): 206.99849621027772, (47, 27795): 200.34979140038618, (47, 27801): 204.0390305265752, (47, 27813): 199.92499607300024, (47, 27816): 201.09127679589838, (47, 27823): 204.22532968037015, (47, 27830): 202.43929815609835, (47, 27884): 180.80547054583263, (47, 27885): 182.132300541312, (47, 27896): 181.50981672489758, (47, 27919): 181.84765633590143, (47, 27922): 181.4439276591388, (47, 27930): 181.4787411306798, (47, 27934): 181.18692777045777, (47, 27935): 180.8335973342542, (47, 27948): 166.32019002570863, (47, 27951): 172.40637406056302, (47, 28061): 133.28054863516718, (47, 28290): 120.40591005881292, (47, 28292): 118.4276803565247, (47, 28293): 119.87990528039201, (47, 28295): 118.8528054386202, (47, 28296): 119.81768595170429, (47, 28297): 121.33212241075863, (47, 28302): 120.39890062933135, (47, 28310): 55.52265275389838, (47, 28313): 55.03749322582768, (47, 28372): 54.65624175790232, (47, 28398): 54.58975760070576, (47, 28399): 54.8815775579065, (47, 28400): 54.4194365239498, (47, 28401): 55.62653051379896, (47, 28445): 55.62821649179985, (47, 28475): 56.66734045271623, (47, 28885): 293.2058371461143, (47, 28886): 292.8335424804367, (47, 28915): 293.26022103948515, (47, 28916): 292.8992760147732, (47, 28917): 292.70418415854965, (47, 28921): 293.9200534840632, (47, 28931): 293.8366955620211, (47, 28945): 292.17023394163385, (47, 28982): 292.55484245948935, (47, 29219): 295.2307919418365, (47, 29228): 293.43691505084394, (47, 29246): 305.25619440317905, (47, 29248): 305.16116826710015, (47, 29282): 302.7229304365394, (47, 29290): 306.3729548005619, (47, 29291): 305.9064800817569, (47, 29292): 306.3533025611672, (47, 29293): 305.40319530496055, (47, 29294): 306.1883087559836, (47, 29298): 305.4934357653278, (47, 29299): 305.43059918434574, (47, 29304): 304.5018997256864, (47, 29317): 302.1965133489087, (47, 29323): 302.015280830137, (47, 29330): 303.12946518713983, (47, 29331): 303.66684931590873, (47, 29344): 295.58303292665266, (47, 29445): 275.3445031289197, (47, 29724): 71.61882911798938, (47, 29738): 71.65876063673296, (47, 29745): 72.11522060951111, (47, 29748): 75.01609831267673, (47, 29750): 76.28927201014194, (47, 29759): 74.61388722068428, (47, 29772): 74.79934098193449, (47, 29781): 74.83968065526862, (47, 29784): 73.57265130766068, (47, 29790): 75.38811790046513, (47, 29811): 76.55560652322498, (47, 29817): 84.39360035091245, (47, 29818): 84.47690483778756, (47, 29929): 70.30463230342464, (47, 30039): 62.96604415411182, (47, 30066): 57.87035455368105, (47, 30116): 63.523800584470564, (47, 30238): 74.7939383328318, (47, 30248): 60.76667910921223, (47, 30260): 59.92293429238069, (47, 30545): 286.7282025675335, (47, 30733): 267.2313612755403, (47, 30756): 263.0618228120517, (47, 30921): 271.97845185304317, (47, 31079): 216.7932990409194, (47, 31149): 215.72495515017627, (47, 31154): 215.53899310585942, (47, 31160): 215.6157890596074, (47, 31163): 215.25422174886987, (47, 31189): 208.28640355710962, (47, 31215): 208.47053562742164, (47, 31259): 206.46518725561793, (47, 31262): 205.77310571862247, (47, 31430): 216.86489870393632, (47, 31568): 194.19206933537745, (47, 31751): 212.23759473410234, (50, 109): 190.10809614516134, (50, 872): 65.29661768846655, (50, 873): 65.42903312418626, (50, 877): 64.96507676956702, (50, 879): 64.94516052332213, (50, 884): 63.88749585177681, (50, 889): 64.16664691824323, (50, 891): 63.9565623198866, (50, 892): 65.14046960459287, (50, 894): 65.29058719555893, (50, 896): 65.84368828487682, (50, 903): 64.49908688169668, (50, 909): 65.6445004425304, (50, 910): 66.07631362694346, (50, 912): 65.91056940530845, (50, 913): 65.59104133103901, (50, 916): 66.02406149708789, (50, 926): 66.62194243054752, (50, 927): 66.66864457878853, (50, 948): 63.979047174793145, (50, 961): 65.71627636610607, (50, 962): 65.99879703624082, (50, 963): 66.22978609580962, (50, 967): 64.72568707191203, (50, 974): 63.68865354197835, (50, 998): 64.44499177071565, (50, 1014): 74.81980917561374, (50, 1086): 76.35304201749452, (50, 1087): 77.7450700837538, (50, 1089): 76.92916753879796, (50, 1090): 76.84986878871382, (50, 1092): 76.98272456762466, (50, 1097): 76.60260508619916, (50, 1107): 77.94181063873799, (50, 1387): 146.7296712217354, (50, 1554): 155.09945219104443, (50, 1827): 75.6929197874505, (50, 1828): 75.88291653971856, (50, 1829): 75.89146060571156, (50, 1830): 75.21094003458505, (50, 1831): 75.36959795372438, (50, 1832): 75.3595401301163, (50, 1833): 75.46696449800811, (50, 1836): 75.50923028690931, (50, 1841): 75.75595600930447, (50, 1843): 75.59053360694266, (50, 1844): 75.56544859490842, (50, 1845): 75.28160785223382, (50, 1847): 74.94336368126105, (50, 1848): 75.1235666816733, (50, 1849): 75.88511226726, (50, 1850): 76.0673318059557, (50, 1851): 74.99592532319929, (50, 1852): 74.7806351783743, (50, 1854): 75.04986976354566, (50, 1856): 74.60929989749121, (50, 1857): 74.98434271244605, (50, 1858): 75.95814502684782, (50, 1861): 75.68013702421563, (50, 1866): 74.39723368073486, (50, 1867): 75.96128568620065, (50, 1868): 76.0181310662479, (50, 1870): 75.25295355526598, (50, 1871): 76.12582539433814, (50, 1875): 75.1954738454968, (50, 1880): 74.93439297812606, (50, 1882): 74.6598109839727, (50, 1883): 76.33382905759167, (50, 1889): 75.425144747498, (50, 1893): 76.28360948464116, (50, 1894): 76.20428272699397, (50, 1899): 75.45745417659197, (50, 1900): 75.64511552637136, (50, 1902): 76.53848676391047, (50, 1905): 76.57713850711167, (50, 1907): 75.49861120775817, (50, 1910): 75.85721337690416, (50, 1917): 77.73727036446317, (50, 1920): 75.71876470144574, (50, 1935): 77.05019304411641, (50, 1937): 77.13589100757376, (50, 1946): 75.67347567775998, (50, 1949): 75.9801176015071, (50, 1950): 74.72723592182975, (50, 1951): 75.19996621746407, (50, 1952): 74.82656960393238, (50, 1953): 75.49337280983646, (50, 1954): 74.93012075656513, (50, 1958): 75.66934969493657, (50, 1960): 75.83564091945094, (50, 1968): 75.90374465544464, (50, 1969): 77.54300697569157, (50, 1974): 77.0730165519335, (50, 1975): 76.91767825063293, (50, 1979): 76.74297430336227, (50, 1980): 76.24606823977854, (50, 1981): 76.67400061261537, (50, 1985): 76.91668459788583, (50, 1994): 73.40634873746161, (50, 2011): 74.49915685827006, (50, 2019): 75.58307609652238, (50, 2020): 75.4318182520498, (50, 2029): 74.44612305280295, (50, 2030): 75.33452461306541, (50, 2032): 74.0678331074407, (50, 2033): 74.80306007918483, (50, 2034): 74.582863586235, (50, 2036): 72.79542397992584, (50, 2037): 73.28584005313655, (50, 2038): 74.35946532917612, (50, 2042): 76.77955710340032, (50, 2050): 75.00591930640213, (50, 2051): 74.74083793282907, (50, 2053): 74.90527922588397, (50, 2054): 75.1088654054971, (50, 2066): 74.65476069684668, (50, 2067): 74.77469613268069, (50, 2071): 73.14454188392716, (50, 2072): 73.71495701345961, (50, 2073): 73.28772999564194, (50, 2074): 73.07701288253118, (50, 2080): 72.03072618294672, (50, 2082): 73.96869636817574, (50, 2083): 74.27892201271494, (50, 2089): 74.00874861502938, (50, 2090): 74.33879993683544, (50, 2092): 74.20989974029929, (50, 2098): 72.6010046173321, (50, 2099): 72.68199504837573, (50, 2101): 72.3410790489749, (50, 2102): 73.70914338869109, (50, 2103): 73.18970582991136, (50, 2104): 72.80352542219686, (50, 2106): 74.32884437252646, (50, 2112): 72.31917534638981, (50, 2113): 73.77211308419065, (50, 2114): 73.73427492113956, (50, 2117): 74.35162188132232, (50, 2123): 81.57083816717957, (50, 2124): 81.8358028896959, (50, 2134): 80.42912296127116, (50, 2138): 81.47018817123445, (50, 2141): 80.7212329582528, (50, 2148): 78.63012148110555, (50, 2150): 79.95726831619625, (50, 2151): 80.0494990727365, (50, 2152): 79.6388998778182, (50, 2153): 78.95401879957085, (50, 2154): 77.99486821811632, (50, 2155): 77.45024118190922, (50, 2156): 77.5426473980841, (50, 2157): 76.31649780107695, (50, 2160): 80.6439715563291, (50, 2161): 79.3423203475697, (50, 2162): 78.08071943556766, (50, 2163): 77.78070495398765, (50, 2164): 77.60818042221, (50, 2168): 78.77438095128026, (50, 2172): 77.89078761025503, (50, 2174): 79.70045174289608, (50, 2178): 77.78326703469591, (50, 2179): 77.51651968005338, (50, 2183): 81.16161801115352, (50, 2185): 81.02371832326826, (50, 2186): 80.89314622104871, (50, 2190): 80.96684169884169, (50, 2192): 80.67505871061198, (50, 2193): 81.32289511172357, (50, 2194): 81.02820673972501, (50, 2195): 80.65253494660952, (50, 2197): 80.57798960848933, (50, 2205): 79.69531167924453, (50, 2207): 78.65115266014753, (50, 2208): 79.1695029397956, (50, 2212): 82.14001959778483, (50, 2214): 70.29642526860195, (50, 2225): 70.11091685106702, (50, 2231): 76.12240109317685, (50, 2278): 71.37481108433438, (50, 2284): 71.5948458648252, (50, 2285): 71.29500609888437, (50, 2291): 68.54158060637185, (50, 2292): 70.30638460517956, (50, 2307): 71.08839396053455, (50, 2313): 67.87823405333127, (50, 2317): 70.45729232756943, (50, 2319): 70.38885421821645, (50, 2321): 70.44809834373143, (50, 2323): 70.85970802035921, (50, 2326): 72.94650706111146, (50, 2327): 72.64198377479381, (50, 2329): 72.38753123452791, (50, 2330): 71.9897291834641, (50, 2332): 72.27706719890587, (50, 2344): 72.16542866228988, (50, 2346): 71.82787553798728, (50, 2361): 74.47333165495544, (50, 2368): 76.40432477946679, (50, 2374): 76.50545151977707, (50, 2375): 76.77512180799374, (50, 2377): 75.82826733919454, (50, 2378): 76.85728933318818, (50, 2379): 76.57736225192926, (50, 2380): 76.91427601169939, (50, 2383): 76.3319507412588, (50, 2385): 76.62231668790737, (50, 2395): 76.92561981868046, (50, 2397): 76.2966872305853, (50, 2398): 75.49691184679786, (50, 2399): 76.05462196383178, (50, 2400): 75.96938448976253, (50, 2402): 75.74214317831438, (50, 2403): 75.98006569937807, (50, 2404): 76.16891884619169, (50, 2405): 75.48231705913238, (50, 2407): 76.2268006464687, (50, 2408): 76.37382586809203, (50, 2409): 75.73906770558929, (50, 2411): 75.46392990457471, (50, 2412): 75.5932542927218, (50, 2413): 75.72005873007038, (50, 2414): 75.32954408236587, (50, 2422): 75.21205895140285, (50, 2424): 75.77387307356533, (50, 2426): 75.9306936824254, (50, 2433): 75.2787864424872, (50, 2436): 74.82049897161006, (50, 2437): 73.52046311029135, (50, 2440): 73.89727774768967, (50, 2445): 77.94097275135435, (50, 2447): 77.32080208122557, (50, 2454): 78.14850927302335, (50, 2455): 78.40810533090466, (50, 2460): 75.57473240054304, (50, 2461): 75.87323096123706, (50, 2471): 79.97537170047941, (50, 2492): 67.17975842616612, (50, 2511): 65.26723898130341, (50, 2523): 66.18967897621263, (50, 2525): 65.40541447060012, (50, 2535): 69.77990434811099, (50, 2537): 69.03873829362084, (50, 2538): 69.74370616056805, (50, 2539): 68.61908773900173, (50, 2540): 70.09233852477693, (50, 2542): 70.30276317609535, (50, 2559): 81.51609338251885, (50, 2575): 79.61798938499058, (50, 2599): 68.81380750426001, (50, 2600): 70.95334527906078, (50, 2607): 70.57363449340527, (50, 2627): 64.46183322534911, (50, 2647): 65.88166060515373, (50, 2674): 65.615486862795, (50, 2681): 65.01907575997978, (50, 2683): 66.06740929283036, (50, 2686): 65.20723193838705, (50, 2689): 77.0891918489262, (50, 2690): 77.08620702085162, (50, 2713): 78.03621006105077, (50, 2714): 78.1081077504208, (50, 2715): 78.43304022980809, (50, 2739): 78.18612958861951, (50, 2740): 76.59263857883106, (50, 2741): 76.78897937036687, (50, 2749): 77.59467941726014, (50, 2750): 77.74288735181976, (50, 2752): 77.99622024737555, (50, 2755): 78.22313148872138, (50, 2758): 78.10928575587, (50, 2759): 78.13104057917724, (50, 2769): 77.80767358765938, (50, 2771): 76.98635655784948, (50, 2779): 76.69015569113752, (50, 2784): 72.89299847296164, (50, 2800): 73.26187543191129, (50, 2802): 75.73142578731513, (50, 2803): 75.66246584139004, (50, 2804): 75.46898032743741, (50, 2805): 75.84988647207213, (50, 2807): 75.87969431555219, (50, 2809): 75.64975533541725, (50, 2812): 73.70575083432932, (50, 2814): 75.25508880791021, (50, 2817): 75.03753012180094, (50, 2819): 76.04978345474821, (50, 2823): 73.5052256873598, (50, 2832): 76.18318161333292, (50, 2836): 74.73487589188662, (50, 2839): 75.92712375077875, (50, 2841): 75.2425277340911, (50, 2843): 75.18759674038164, (50, 2846): 74.838245673627, (50, 2849): 76.33222804368629, (50, 2852): 76.03163050531899, (50, 2853): 76.46820241034037, (50, 2876): 76.42575427148705, (50, 2877): 77.57000789377146, (50, 2885): 77.64792642004512, (50, 2918): 76.58455476295535, (50, 2921): 77.00624843483062, (50, 2925): 75.28845845623881, (50, 2926): 74.89768733602506, (50, 2930): 75.51856707769069, (50, 2931): 75.30116138629859, (50, 2938): 76.48484633348613, (50, 2940): 78.44394544188695, (50, 2947): 76.92715237737592, (50, 2949): 75.74327446556569, (50, 2950): 75.85875588413981, (50, 2952): 75.6120395278942, (50, 2958): 75.60794790879604, (50, 2959): 75.96770288291697, (50, 2960): 76.46693415138087, (50, 2961): 76.15766703378371, (50, 2963): 75.34066410505744, (50, 2968): 75.4346035143367, (50, 2976): 75.3399559558284, (50, 2981): 69.98528738751209, (50, 2982): 69.75148646499616, (50, 2984): 69.4847991062116, (50, 3003): 68.95314040362356, (50, 3046): 67.22189546895078, (50, 3050): 68.91204464865385, (50, 3051): 69.15204839881093, (50, 3053): 68.56381272167397, (50, 3069): 71.36668083883862, (50, 3071): 68.7396645856334, (50, 3080): 77.58638798248245, (50, 3199): 67.72354713702312, (50, 3200): 67.11260147811993, (50, 3205): 70.70309388541621, (50, 3209): 67.4094800371816, (50, 3215): 67.17497310709783, (50, 3217): 66.4558786541469, (50, 3249): 67.2704216478672, (50, 3263): 72.71631641847249, (50, 3289): 69.07810184885562, (50, 3301): 69.16591016245935, (50, 3302): 68.93648062474492, (50, 3307): 68.62229775904488, (50, 3310): 69.4755024917237, (50, 3391): 70.87982308655694, (50, 3509): 48.9571023098071, (50, 3510): 49.4409101415631, (50, 3511): 49.26103517430076, (50, 3512): 49.68620653312198, (50, 3514): 49.702342509280314, (50, 3519): 47.160935174939276, (50, 3536): 48.36364379939417, (50, 3545): 47.76775751068491, (50, 3548): 48.703686887424944, (50, 3572): 47.910742415562865, (50, 3581): 48.03171477383648, (50, 3583): 48.93583005153588, (50, 3601): 46.047079750144384, (50, 3656): 46.407772665564146, (50, 3669): 46.64560683161936, (50, 3670): 46.167405695155225, (50, 3695): 49.01519647482169, (50, 3696): 48.67072263868294, (50, 3782): 51.77886573798678, (50, 3792): 51.71541516573305, (50, 3989): 260.5643734190619, (50, 4008): 263.0561689416289, (50, 4031): 262.4282478836087, (50, 4045): 261.9878606953702, (50, 4144): 262.55746442616413, (50, 4145): 260.5219754136106, (50, 4164): 261.7050358180514, (50, 4168): 261.14590208241833, (50, 4173): 261.0957867292682, (50, 4181): 259.57370098611574, (50, 4228): 257.64287633664094, (50, 4248): 257.6842012593505, (50, 4254): 245.99945779931932, (50, 4260): 245.849665829643, (50, 4262): 246.85846422595984, (50, 4273): 246.53867333839247, (50, 4319): 239.22267020993422, (50, 4326): 238.90632807518867, (50, 4328): 238.96416436795923, (50, 4334): 239.62439394916885, (50, 4335): 239.45885808956962, (50, 4372): 238.03927790155478, (50, 4413): 246.4519781689623, (50, 4434): 237.71179951724736, (50, 4447): 238.9208262461957, (50, 4452): 237.81671676007002, (50, 4463): 219.74321176666487, (50, 4465): 220.37522123663547, (50, 4619): 247.0902050240622, (50, 4645): 249.05875812695805, (50, 4657): 248.70770476185092, (50, 4666): 247.92048568334602, (50, 4676): 249.25601243093152, (50, 4678): 249.578131761058, (50, 4689): 248.60706954452024, (50, 4704): 255.22692031482066, (50, 4726): 269.82984731007576, (50, 4727): 269.5545698084942, (50, 4730): 269.02667570610316, (50, 4731): 269.13860676432046, (50, 4734): 269.6651575190618, (50, 4735): 269.3704242941446, (50, 4736): 269.4725792775711, (50, 4737): 268.96958340806486, (50, 4738): 269.00754620992006, (50, 4756): 269.26473186721245, (50, 4760): 268.04987066066474, (50, 4761): 268.2727321350769, (50, 4762): 267.6326036970802, (50, 4765): 268.16540659169374, (50, 4773): 270.4051619479735, (50, 4774): 270.0968712118431, (50, 4790): 270.23159886737926, (50, 4795): 270.0067895084528, (50, 4799): 270.1826949262509, (50, 4801): 270.6733904148969, (50, 4804): 270.17861594592284, (50, 4805): 269.99294473390677, (50, 4806): 269.89983145634574, (50, 4815): 269.58072502427916, (50, 4816): 270.29901550001273, (50, 4817): 270.362989601912, (50, 4826): 269.9745356728824, (50, 4830): 269.55247243693873, (50, 4839): 268.84839983019083, (50, 4840): 269.0636655443842, (50, 4841): 268.4587905172354, (50, 4846): 268.2799483558344, (50, 4848): 268.1561390293618, (50, 4850): 268.3958643768533, (50, 4871): 265.4813830138892, (50, 4883): 267.82860030220525, (50, 4900): 266.7068054136008, (50, 4901): 266.3159075980504, (50, 4917): 245.78428346791625, (50, 4931): 243.69860598439683, (50, 4944): 246.0685162200706, (50, 4956): 244.03329338697256, (50, 4958): 243.878359237889, (50, 4959): 243.41753854891027, (50, 4961): 244.49425925705273, (50, 4966): 243.46872608716242, (50, 5207): 241.1478295975838, (50, 5272): 204.2359659960746, (50, 5283): 204.96752316998547, (50, 5287): 205.9267284832687, (50, 5289): 206.23992716196517, (50, 5293): 204.57464738744812, (50, 5295): 206.65155896249098, (50, 5296): 206.5093266119317, (50, 5298): 206.41368878193435, (50, 5303): 206.91831801305526, (50, 5305): 203.56007716383195, (50, 5306): 202.8038624807791, (50, 5307): 203.16484695978465, (50, 5308): 203.85937019730662, (50, 5313): 203.98823841573142, (50, 5314): 204.50356165040665, (50, 5317): 203.78119738282095, (50, 5319): 206.17246061228974, (50, 5324): 205.85072585851103, (50, 5326): 205.65130685847907, (50, 5348): 202.5227389997775, (50, 5351): 202.89381551818147, (50, 5399): 206.474315468878, (50, 5413): 203.56040004278958, (50, 5422): 207.0014373380522, (50, 5445): 205.24757672068893, (50, 5448): 204.53827815116617, (50, 5456): 204.2373060704552, (50, 5467): 204.86094307037374, (50, 5624): 197.505137858962, (50, 5671): 222.25744511070212, (50, 5672): 221.2997303264321, (50, 5797): 233.77650507692428, (50, 5871): 215.30895461636828, (50, 5976): 206.84659650506757, (50, 6118): 23.299634631619565, (50, 6248): 39.323419225220334, (50, 6345): 160.6801501908722, (50, 6352): 158.27881996905273, (50, 6354): 161.26811925258897, (50, 6359): 161.74236164363015, (50, 6376): 158.66903791614214, (50, 6378): 160.98291196606755, (50, 6381): 161.5461809652752, (50, 6383): 160.17031089837337, (50, 6396): 161.2912625210822, (50, 6399): 160.7118609809599, (50, 6408): 158.36376921986624, (50, 6409): 159.5001114088737, (50, 6419): 155.63111513001735, (50, 6422): 158.6810914078633, (50, 6423): 158.48722414682186, (50, 6424): 161.04330327090824, (50, 6439): 160.5865651587638, (50, 6464): 159.92482207064796, (50, 6465): 159.6772649569602, (50, 6469): 159.96813901611912, (50, 6470): 159.81928405834014, (50, 6472): 162.55678748213387, (50, 6480): 162.07731588463145, (50, 6486): 163.58069255061164, (50, 6497): 163.0743669778037, (50, 6503): 160.16469244527727, (50, 6508): 160.28459162620175, (50, 6509): 160.77525720310624, (50, 6521): 162.40127479904828, (50, 6544): 162.28102859012668, (50, 6552): 159.13741936084327, (50, 6553): 158.7657172335999, (50, 6554): 158.38698500059724, (50, 6578): 159.75290958024178, (50, 6582): 159.52386950811527, (50, 6601): 159.93214051176622, (50, 6609): 162.8928913210429, (50, 6610): 163.00684695419648, (50, 6611): 163.06237266930634, (50, 6614): 162.85837068767998, (50, 6615): 162.93261411429836, (50, 6616): 163.3467109351161, (50, 6617): 163.16631271140895, (50, 6618): 163.74702247983353, (50, 6619): 162.58934237775836, (50, 6620): 163.36854342514457, (50, 6621): 163.05269344064234, (50, 6622): 163.11744569738764, (50, 6623): 162.83478290081743, (50, 6624): 162.56262953698345, (50, 6625): 162.49648053442093, (50, 6626): 162.5675966319056, (50, 6627): 162.7727199903977, (50, 6628): 163.317989727971, (50, 6629): 162.66717445154214, (50, 6630): 162.20611723425637, (50, 6632): 162.6269969545152, (50, 6634): 161.86737288070475, (50, 6635): 162.93029466822014, (50, 6636): 163.36924618169127, (50, 6637): 162.23061078224234, (50, 6638): 162.25415554208058, (50, 6639): 162.81038214574818, (50, 6640): 162.30284679864536, (50, 6641): 163.0565344451637, (50, 6642): 162.2687147477825, (50, 6643): 162.52564592256056, (50, 6645): 162.6383854953843, (50, 6646): 163.62081717899528, (50, 6647): 162.36082240995884, (50, 6653): 162.91524105937648, (50, 6655): 162.81135616001316, (50, 6658): 161.84758172309367, (50, 6662): 162.25872327167912, (50, 6819): 144.27266653356344, (50, 6996): 151.14120001321845, (50, 7059): 155.39243174349932, (50, 7187): 150.87278755873578, (50, 7304): 140.03285206947322, (50, 7528): 151.7706390271009, (50, 7720): 176.19653020029153, (50, 7793): 176.03604451331532, (50, 7807): 176.26145764874454, (50, 7808): 175.99885717297684, (50, 7831): 165.34231509924922, (50, 7850): 169.300010545509, (50, 7852): 168.34612416575507, (50, 8012): 174.5520635757323, (50, 8125): 180.8687773882973, (50, 8208): 184.06777334614756, (50, 8392): 169.02667169595594, (50, 8651): 123.80988462544038, (50, 9088): 142.54401819015925, (50, 9443): 118.21258968086936, (50, 9444): 118.90582453671252, (50, 9828): 103.93825245284242, (50, 9868): 99.73510163351972, (50, 10180): 181.49750580944087, (50, 10256): 192.57126420326472, (50, 10276): 187.09259333851554, (50, 10378): 187.3500634197035, (50, 10676): 179.93732471126617, (50, 10714): 173.45127760933755, (50, 10730): 173.06886665489824, (50, 10862): 184.7144555639638, (50, 10881): 186.42125834058666, (50, 10883): 186.24654328054285, (50, 10885): 184.34373831504948, (50, 10891): 185.97858011058298, (50, 10909): 185.7939454248688, (50, 10911): 185.99829045135087, (50, 10913): 185.61557489313716, (50, 10915): 185.57987141213238, (50, 10919): 185.80251171324005, (50, 11037): 174.86443952080987, (50, 11039): 170.31059753068806, (50, 11516): 282.58003861599826, (50, 11856): 239.88595386875087, (50, 11857): 239.65981165282744, (50, 11861): 239.7912827823078, (50, 11881): 239.12186339390522, (50, 11902): 237.26495158197898, (50, 11911): 236.76357222071792, (50, 11914): 237.09369221425968, (50, 11922): 238.53089111246044, (50, 11924): 238.92617201055708, (50, 11926): 238.3815119495091, (50, 11950): 239.25506733698157, (50, 11963): 241.0287726859129, (50, 11983): 239.52846401408573, (50, 11985): 241.93402310115033, (50, 12009): 241.3251530901208, (50, 12010): 240.13349451590287, (50, 12018): 240.30461412250287, (50, 12020): 240.6839831430999, (50, 12021): 240.8627858489575, (50, 12024): 242.06295491199205, (50, 12025): 241.71148708200909, (50, 12027): 241.4139023870695, (50, 12031): 239.9249888810152, (50, 12032): 240.3845734136699, (50, 12035): 241.18370631095362, (50, 12041): 242.23925257509055, (50, 12045): 225.30543958730928, (50, 12145): 232.70051581654897, (50, 12275): 260.7487461479273, (50, 12294): 257.19852735108725, (50, 12358): 266.82366712633524, (50, 12463): 270.34743240676625, (50, 12465): 270.2136360757729, (50, 12482): 272.18527270245465, (50, 12503): 271.8799133766789, (50, 12506): 272.34756304668815, (50, 12549): 271.66359586945936, (50, 12559): 271.2411847490449, (50, 12569): 271.5081221885492, (50, 12572): 271.86651843870277, (50, 12574): 271.153762020313, (50, 12576): 272.1099240621806, (50, 12591): 272.21465986982986, (50, 12608): 275.2017421225862, (50, 12696): 270.76216102133486, (50, 12710): 273.68213521038723, (50, 12728): 272.11137453976704, (50, 12766): 196.41519874278526, (50, 12771): 193.69266553448543, (50, 12790): 193.21678358005312, (50, 12795): 192.04056884205517, (50, 12797): 188.1398011526703, (50, 12798): 188.75620845801635, (50, 12811): 192.14425755757475, (50, 12830): 190.87981532751292, (50, 12848): 191.732448625035, (50, 12850): 192.17717595444535, (50, 12852): 190.7959961067185, (50, 12854): 190.2734811271175, (50, 12859): 192.32124443147623, (50, 12861): 189.39289992693116, (50, 12865): 192.6723441932455, (50, 12866): 192.4790954240354, (50, 12867): 193.4584457347932, (50, 12874): 192.9727001522329, (50, 12875): 193.40076875117256, (50, 12881): 191.6914746411148, (50, 12883): 192.34706183841678, (50, 12885): 193.72702711854507, (50, 12888): 192.09704346235864, (50, 12889): 192.00052182006354, (50, 12892): 193.05594325786387, (50, 12893): 192.06894127756993, (50, 12896): 192.43339177143565, (50, 12906): 192.78075595236302, (50, 13018): 186.84941865947204, (50, 13071): 186.6640987130376, (50, 13131): 183.4407002765078, (50, 13146): 187.1444674205285, (50, 13159): 181.03443948038245, (50, 13193): 182.84438932543074, (50, 13198): 177.20827054692018, (50, 13292): 184.3514893627612, (50, 13296): 186.86982273092693, (50, 13406): 172.65017840464517, (50, 13407): 172.39401259384212, (50, 13417): 171.51429055641958, (50, 13418): 172.11335177044444, (50, 13438): 175.12224742530847, (50, 13442): 175.79662705827602, (50, 13443): 175.26078100932762, (50, 13764): 128.39421578937282, (50, 13766): 129.06830836701278, (50, 13771): 128.43443208770464, (50, 13783): 127.80848452164265, (50, 13784): 129.79612284621902, (50, 13792): 127.18972126896095, (50, 13824): 127.34681437346467, (50, 14017): 131.42761432332392, (50, 14870): 184.05054910111448, (50, 14997): 148.06593310218926, (50, 15000): 148.33744815872527, (50, 15003): 148.99424536374926, (50, 15006): 149.10066422946005, (50, 15007): 149.57560314572498, (50, 15056): 150.12265546495036, (50, 15063): 149.83907207094413, (50, 15069): 149.9256733245811, (50, 15076): 149.7885836132378, (50, 15086): 148.10742068757065, (50, 15087): 147.89580101380622, (50, 15111): 146.33200801108003, (50, 15116): 147.25011901123779, (50, 15722): 135.06623152733317, (50, 15998): 133.17152564460204, (50, 16073): 50.01360386019732, (50, 16939): 47.52225795444462, (50, 16940): 47.23172462391814, (50, 16951): 46.59661651985412, (50, 16963): 46.863058987647385, (50, 16965): 47.65852741852806, (50, 16969): 46.96827602438669, (50, 16970): 47.337370455942235, (50, 16971): 46.65880028400967, (50, 16973): 46.26575429987369, (50, 16974): 47.65126922169847, (50, 16976): 47.609819047192346, (50, 16978): 47.23701808182451, (50, 16980): 48.15717957215295, (50, 16982): 47.29136867548467, (50, 17045): 55.0451369105403, (50, 17048): 55.98325698517081, (50, 17304): 254.60994476963924, (50, 17305): 253.90208154897948, (50, 17330): 254.41088329447976, (50, 17334): 253.7785588314739, (50, 17343): 255.01702529271654, (50, 17345): 253.47635158799432, (50, 17347): 254.17399068196676, (50, 17351): 252.58728342612656, (50, 17372): 253.57864020031576, (50, 17373): 255.00663957064825, (50, 17377): 255.0848330305832, (50, 17382): 254.09779292747632, (50, 17383): 254.37169881579942, (50, 17389): 253.76728745559757, (50, 17400): 254.81636192625996, (50, 17401): 254.8394450443688, (50, 17402): 254.84874715041244, (50, 17403): 254.92531773230357, (50, 17440): 253.24346870998207, (50, 17455): 254.6660119979195, (50, 17491): 254.56034524643982, (50, 17507): 253.80654627442686, (50, 17509): 254.434745517076, (50, 17590): 251.91093999958176, (50, 17615): 250.53361840560206, (50, 17642): 250.96021714508038, (50, 17643): 250.80767210441243, (50, 17668): 250.57599403218995, (50, 17721): 249.83818876330443, (50, 17754): 255.30503619670287, (50, 17769): 254.29875683722193, (50, 17776): 251.57119499706218, (50, 17804): 255.2602148461585, (50, 17809): 255.82608932766377, (50, 17824): 255.62728283188514, (50, 17837): 253.1879323059239, (50, 17838): 253.0962479121423, (50, 17862): 252.60246199972804, (50, 17866): 253.87883717826037, (50, 17872): 252.2896042360432, (50, 17873): 251.28011005053222, (50, 17881): 252.80622267296516, (50, 17947): 63.019748729886736, (50, 17951): 62.72345580262394, (50, 17953): 63.07831387309465, (50, 17954): 63.36484124327694, (50, 17959): 62.249943300981904, (50, 17963): 61.43620235299836, (50, 18000): 61.58382562095152, (50, 18001): 62.11844283987015, (50, 18111): 83.95641047092137, (50, 18148): 83.66236849541255, (50, 18166): 84.39634627268966, (50, 18189): 82.27159629831857, (50, 18239): 255.39611323670687, (50, 18240): 255.35565605050533, (50, 18245): 255.43153162679712, (50, 18247): 255.27185525538417, (50, 18251): 255.3883479431504, (50, 18256): 255.475303910114, (50, 18258): 255.31389331269563, (50, 18259): 255.32126420929345, (50, 18260): 255.35091499344645, (50, 18262): 255.43217440081295, (50, 18263): 255.49330094627024, (50, 18264): 255.52495671475836, (50, 18266): 255.44414816180287, (50, 18267): 255.4798853305726, (50, 18268): 255.48482363432709, (50, 18269): 255.55244442794887, (50, 18275): 255.52038857873526, (50, 18285): 255.52751584491912, (50, 18308): 254.81337891570666, (50, 18313): 254.47622733507083, (50, 18314): 254.52495819482408, (50, 18315): 255.642512149365, (50, 18316): 255.59046971181567, (50, 18317): 255.6192455178758, (50, 18320): 255.7119820962902, (50, 18321): 255.7073458367308, (50, 18322): 255.76191242131077, (50, 18324): 255.8710327138304, (50, 18325): 256.10373146590103, (50, 18326): 256.01911836631587, (50, 18327): 255.6076887203234, (50, 18329): 256.2588350999379, (50, 18330): 256.0015649243361, (50, 18331): 255.86810533227316, (50, 18332): 255.70725294594106, (50, 18333): 256.0175973305617, (50, 18336): 255.954742926451, (50, 18337): 256.06270155672536, (50, 18403): 255.69022494963747, (50, 18432): 251.19619428026627, (50, 18451): 254.2353289027511, (50, 18466): 257.3150760164144, (50, 18481): 255.82267035107614, (50, 18483): 255.7908405761425, (50, 18484): 255.68712740649244, (50, 18485): 255.40691064187726, (50, 18486): 255.86274707151935, (50, 18487): 255.6030432666394, (50, 18489): 255.72015327298507, (50, 18490): 256.10297609597563, (50, 18491): 256.24327113247836, (50, 18492): 255.27698228514424, (50, 18493): 255.85041126592358, (50, 18494): 255.63761029842064, (50, 18495): 256.0031567900759, (50, 18496): 255.83027681827375, (50, 18497): 255.5722866165104, (50, 18498): 255.51273562000347, (50, 18499): 255.71937407865394, (50, 18501): 255.62537786347326, (50, 18502): 255.49676505619607, (50, 18503): 255.3598213000307, (50, 18504): 255.84951230414725, (50, 18506): 255.7353575529613, (50, 18507): 255.63051507480105, (50, 18508): 255.72110079365265, (50, 18509): 255.7535529652365, (50, 18510): 255.40708922252932, (50, 18511): 255.9543412804998, (50, 18512): 255.73831757394606, (50, 18515): 255.90672302958208, (50, 18516): 256.020343011066, (50, 18517): 255.9027070559289, (50, 18518): 256.10228943598156, (50, 18519): 255.86004688259874, (50, 18520): 255.64437252328264, (50, 18522): 256.364414549525, (50, 18523): 256.4282341651751, (50, 18532): 256.6649124889509, (50, 18535): 256.2083409979993, (50, 18537): 255.95415198098593, (50, 18539): 256.02513734795383, (50, 18540): 256.0735717492409, (50, 18541): 256.21426076305744, (50, 18542): 256.30033661180016, (50, 18543): 255.8866758671818, (50, 18546): 256.14101207920845, (50, 18555): 256.54262838633065, (50, 18556): 256.63884736605706, (50, 18565): 256.68115044146185, (50, 18567): 256.8650889181411, (50, 18568): 256.61763706868635, (50, 18577): 258.17395923149394, (50, 18583): 257.81967927918396, (50, 18605): 258.0349775004945, (50, 18608): 257.13434436150675, (50, 18616): 259.4950403408088, (50, 18618): 260.796560599385, (50, 18625): 260.12552933005406, (50, 18645): 258.9275672252389, (50, 18646): 259.29489744615086, (50, 18653): 258.49508443766587, (50, 18654): 259.50355889051315, (50, 18655): 258.89126344489557, (50, 18666): 262.5106994916767, (50, 18837): 254.45999791552111, (50, 18974): 253.43086075652337, (50, 18999): 254.05637659033383, (50, 19000): 254.42162816398024, (50, 19174): 235.01606680246044, (50, 19342): 241.8208564722108, (50, 19455): 239.19634992429485, (50, 19555): 220.3876068106716, (50, 19564): 220.82415761230425, (50, 19573): 220.18427461164254, (50, 19586): 219.94015249711012, (50, 19605): 220.3315548148328, (50, 19611): 220.78749791561148, (50, 19614): 220.75360121935475, (50, 19641): 229.15994929572474, (50, 19702): 228.8167851165243, (50, 19713): 228.24106709734554, (50, 19731): 218.38297200084534, (50, 19819): 236.01858486401238, (50, 19893): 224.76480438960894, (50, 19899): 229.0849860423605, (50, 19929): 225.83663122113364, (50, 19951): 234.21281589196772, (50, 19962): 226.63990280018925, (50, 19970): 228.2409878999768, (50, 19971): 228.3345802309832, (50, 19972): 227.66920886015836, (50, 19975): 227.29842315825329, (50, 19978): 235.75838429667715, (50, 19987): 235.87035335537473, (50, 19989): 233.56591546727023, (50, 20039): 236.27883451224787, (50, 20043): 237.19864043723487, (50, 20047): 236.42369661092272, (50, 20052): 233.90917615608046, (50, 20054): 234.1304785894855, (50, 20085): 245.410321275352, (50, 20104): 246.12336735044133, (50, 20132): 241.7974171474069, (50, 20203): 224.80212567849824, (50, 20280): 224.00879417134524, (50, 20285): 223.83234824506772, (50, 20290): 224.38265590127696, (50, 20297): 223.590100590667, (50, 20309): 236.67948818520065, (50, 20453): 248.3387744831435, (50, 20485): 218.61888977958287, (50, 20520): 216.60345491683617, (50, 20526): 216.01552513295763, (50, 20698): 111.5522996007328, (50, 20868): 90.0071440248984, (50, 21042): 195.54808390144274, (50, 21057): 200.12498389629647, (50, 21066): 198.0406839683172, (50, 21075): 196.94908295159195, (50, 21093): 196.1180341674806, (50, 21098): 199.69665209865963, (50, 21127): 196.0443370459578, (50, 21130): 197.0184720065432, (50, 21144): 196.67644956340337, (50, 21146): 195.744076639648, (50, 21147): 196.53675035997304, (50, 21148): 197.4064689991713, (50, 21153): 194.69980310268588, (50, 21293): 203.430453763967, (50, 21426): 200.3432692063998, (50, 21442): 204.92911792145975, (50, 21451): 205.38056571550652, (50, 21466): 202.7170637932634, (50, 21469): 203.4851368627148, (50, 21471): 202.32359577664937, (50, 21473): 202.98064472844754, (50, 21475): 202.4173728963536, (50, 21482): 203.89666656467892, (50, 21484): 203.77553587586056, (50, 21488): 203.3051453680475, (50, 21494): 202.51558548764163, (50, 21498): 203.06167411701213, (50, 21500): 202.27915362199738, (50, 21514): 204.1653991023311, (50, 21537): 202.35251706197573, (50, 21662): 205.10983996026167, (50, 21691): 202.18961931802824, (50, 21757): 196.19132557488797, (50, 21777): 187.43466615111257, (50, 21778): 186.7041207427947, (50, 21779): 187.22254122883365, (50, 21790): 188.1389926482505, (50, 21802): 188.31480579587804, (50, 21824): 189.1832906664051, (50, 21874): 187.54816682439275, (50, 21879): 187.32336890899902, (50, 21983): 189.30479895049763, (50, 22002): 197.91074769646198, (50, 22132): 190.58042814667672, (50, 22261): 110.25571606916112, (50, 22298): 112.39370404347049, (50, 22339): 109.8812798385378, (50, 22508): 120.41523152102037, (50, 22841): 83.31227010477228, (50, 22842): 83.1242561860138, (50, 22874): 80.92698616530018, (50, 22941): 81.73801023425534, (50, 22956): 82.5125082838211, (50, 22960): 83.24975640365363, (50, 22968): 81.65390731992855, (50, 22970): 82.27110544550139, (50, 22974): 81.24169814986489, (50, 22980): 82.40278642148739, (50, 23025): 80.2739052086138, (50, 23028): 79.61229318679628, (50, 23081): 79.45356397312443, (50, 23104): 74.66944404274629, (50, 23147): 68.91095408654503, (50, 23298): 217.4854801450871, (50, 23376): 215.4197283276088, (50, 23381): 214.666041445994, (50, 23529): 219.1940917328346, (50, 23556): 217.93850562505818, (50, 23718): 215.82392250341806, (50, 24001): 229.63510905551263, (50, 24094): 234.2746540526348, (50, 24129): 236.3304653759931, (50, 24174): 232.39616383675656, (50, 24235): 237.18447491699283, (50, 24259): 238.92648420181646, (50, 24260): 238.8129502816058, (50, 24261): 238.33984012650097, (50, 24305): 241.18093146553036, (50, 24306): 241.62352315234588, (50, 24307): 240.99800086700418, (50, 24308): 234.21350160299409, (50, 24498): 245.70701555493537, (50, 24499): 245.76814730682514, (50, 24500): 245.3699031925778, (50, 24668): 241.9306684877865, (50, 24711): 248.6669025837756, (50, 24756): 250.38748124265862, (50, 24788): 250.83538746504576, (50, 24809): 248.8873038610107, (50, 24813): 249.464032495073, (50, 24821): 249.26016664401328, (50, 24825): 249.473253116067, (50, 24832): 248.7057985842287, (50, 24833): 249.03848648374552, (50, 24835): 249.38880063649628, (50, 24837): 249.87387913486492, (50, 24840): 248.67721114939192, (50, 24841): 249.14381842899488, (50, 24844): 248.72344918798157, (50, 24845): 248.9051392570997, (50, 24846): 249.04719224987753, (50, 24849): 249.24342006605, (50, 24850): 249.60350000915068, (50, 24863): 244.7528458003242, (50, 24866): 245.33548227273783, (50, 24885): 246.14399478057453, (50, 24886): 246.26334100268406, (50, 24889): 247.32046222612104, (50, 24903): 247.71663507231847, (50, 24909): 245.38604357298667, (50, 24999): 270.29425486837135, (50, 25019): 269.34206031850704, (50, 25028): 270.00384622222117, (50, 25137): 226.31342213346605, (50, 25145): 227.11537399526964, (50, 25208): 237.08732835466546, (50, 25233): 236.02216429854874, (50, 25371): 225.87288153906485, (50, 25377): 223.4260510864775, (50, 25828): 181.70397836108543, (50, 25851): 174.8667356562567, (50, 25874): 181.0268582522108, (50, 25898): 184.25520379628256, (50, 25946): 181.02721511330427, (50, 26047): 195.21794752554186, (50, 26066): 207.8558533981065, (50, 26197): 199.27802317429746, (50, 26212): 163.84745224961773, (50, 26253): 162.12469470700267, (50, 26254): 162.6861430533603, (50, 26257): 163.58917103929437, (50, 26258): 162.55758242593882, (50, 26260): 163.06525801107085, (50, 26266): 161.71936382624835, (50, 26267): 162.4291586063713, (50, 26271): 162.5344751004506, (50, 26304): 168.43213164848854, (50, 26305): 168.17252610785744, (50, 26363): 180.35067281376743, (50, 26441): 128.01287723120222, (50, 26442): 127.79734861145366, (50, 26450): 128.4149084992948, (50, 26459): 129.81952348077104, (50, 26462): 130.3374364166196, (50, 26467): 128.83527803263289, (50, 26471): 128.551289508787, (50, 26472): 128.39207138690395, (50, 26473): 128.2124984611294, (50, 26476): 126.43767490654652, (50, 26485): 128.87729181096333, (50, 26493): 128.15999874072585, (50, 26524): 130.7174165110481, (50, 26525): 130.4031936000424, (50, 26556): 128.8216842191685, (50, 26560): 130.02058689828198, (50, 26561): 130.61024661395626, (50, 26564): 128.64864860949024, (50, 26569): 130.31169600334235, (50, 26570): 130.00664779795778, (50, 26573): 129.31281092249282, (50, 26581): 128.78333193709454, (50, 26583): 129.2345912905716, (50, 26593): 128.09479973072746, (50, 26837): 128.17526029051137, (50, 26844): 128.0996238912463, (50, 26863): 126.93460560499271, (50, 26893): 126.1360600457456, (50, 26902): 125.98625548925857, (50, 26905): 127.34858278415798, (50, 26912): 126.85042132538057, (50, 26921): 126.6306959646672, (50, 26922): 125.09468305686636, (50, 27212): 155.32420313184934, (50, 27218): 156.5907534364047, (50, 27239): 154.97715349569944, (50, 27257): 154.59565956898072, (50, 27274): 154.71821206122993, (50, 27279): 154.25449670604795, (50, 27282): 154.33572393492236, (50, 27283): 155.2163559969453, (50, 27285): 154.40166216684818, (50, 27286): 153.6506138177418, (50, 27290): 154.33202998460465, (50, 27295): 155.08468036840597, (50, 27300): 154.89132355935203, (50, 27344): 152.99736674228345, (50, 27366): 152.43336532006677, (50, 27383): 153.4052225596289, (50, 27398): 154.47053511044368, (50, 27406): 154.8845063192325, (50, 27407): 155.2422403963177, (50, 27426): 158.51936510363038, (50, 27432): 157.8690923178554, (50, 27460): 158.69341269664915, (50, 27523): 145.05255358226987, (50, 27545): 152.5841285243917, (50, 27602): 149.8651337185027, (50, 27606): 150.5101633197011, (50, 27646): 141.1234117698599, (50, 27667): 140.52624446538564, (50, 27672): 140.87274842790006, (50, 27674): 140.73364660589007, (50, 27688): 142.1326327123836, (50, 27692): 140.35040854493346, (50, 27693): 140.35240822192966, (50, 27705): 139.92978609552787, (50, 27712): 139.56713292158628, (50, 27786): 165.13159820215836, (50, 27790): 170.05978152313426, (50, 27791): 170.78087003934598, (50, 27795): 164.58598165761657, (50, 27801): 167.79985869450607, (50, 27813): 164.59664126163983, (50, 27816): 165.55965663662099, (50, 27823): 167.9673630922684, (50, 27830): 166.66495672795304, (50, 27884): 138.1148309650265, (50, 27885): 140.74767173270752, (50, 27896): 139.3444524160786, (50, 27919): 139.64766337089634, (50, 27922): 139.37807378297927, (50, 27930): 139.01119564920577, (50, 27934): 138.75144874357508, (50, 27935): 138.41461360375465, (50, 27948): 129.909079482848, (50, 27951): 136.48070294926578, (50, 28061): 86.58602888513717, (50, 28290): 90.44236690593385, (50, 28292): 88.70919945033833, (50, 28293): 89.95101250098264, (50, 28295): 88.64680848997982, (50, 28296): 89.77872906321534, (50, 28297): 91.2285409033263, (50, 28302): 90.06079638937719, (50, 28310): 12.5, (50, 28313): 12.5, (50, 28372): 12.5, (50, 28398): 12.5, (50, 28399): 12.5, (50, 28400): 12.5, (50, 28401): 12.5, (50, 28445): 12.5, (50, 28475): 12.5, (50, 28885): 237.92596585609817, (50, 28886): 237.55630630577778, (50, 28915): 237.99224679852531, (50, 28916): 237.62849020035472, (50, 28917): 237.43598309065027, (50, 28921): 238.63757764976597, (50, 28931): 238.55644461548738, (50, 28945): 236.93288008173968, (50, 28982): 237.30072083410278, (50, 29219): 240.0679489879763, (50, 29228): 238.27328380621273, (50, 29246): 250.16699834619834, (50, 29248): 250.10175124767824, (50, 29282): 247.65182481569062, (50, 29290): 251.25712345137367, (50, 29291): 250.7973202259834, (50, 29292): 251.24177175785155, (50, 29293): 250.28896954905107, (50, 29294): 251.08792101251265, (50, 29298): 250.38661813006138, (50, 29299): 250.3310069209004, (50, 29304): 249.3835562191987, (50, 29317): 247.06282899016216, (50, 29323): 246.87966580167125, (50, 29330): 248.0023171442757, (50, 29331): 248.53813200167403, (50, 29344): 240.47159595731983, (50, 29445): 220.36618182793399, (50, 29724): 89.05007363579102, (50, 29738): 89.30376608207388, (50, 29745): 88.90384692590386, (50, 29748): 90.78580722839295, (50, 29750): 91.9309664826803, (50, 29759): 90.23099781371413, (50, 29772): 91.17747645723303, (50, 29781): 91.02027565022489, (50, 29784): 90.11135770743094, (50, 29790): 91.53429772093105, (50, 29811): 91.77945505809495, (50, 29817): 98.18811395096728, (50, 29818): 98.07651882405908, (50, 29929): 87.7500529449535, (50, 30039): 86.74682603179147, (50, 30066): 82.03349637080986, (50, 30116): 76.56318050223148, (50, 30238): 71.62440731074885, (50, 30248): 68.08830633602052, (50, 30260): 67.69727547550816, (50, 30545): 231.4324415806183, (50, 30733): 211.93390474787537, (50, 30756): 207.80936904143036, (50, 30921): 216.69510159641789, (50, 31079): 161.96757182257997, (50, 31149): 160.6770659407035, (50, 31154): 160.51983656905136, (50, 31160): 160.56274808786597, (50, 31163): 160.23149454518835, (50, 31189): 153.1262867533524, (50, 31215): 153.3379992909653, (50, 31259): 151.4385383342108, (50, 31262): 150.7222057499965, (50, 31430): 162.17207812024807, (50, 31568): 139.41062278638074, (50, 31751): 157.4248602561547, (53, 109): 261.01852680967636, (53, 872): 85.09591174851556, (53, 873): 84.34901951716128, (53, 877): 84.25981939908662, (53, 879): 84.11287314120362, (53, 884): 84.05071171101784, (53, 889): 83.75028429046948, (53, 891): 84.39855360041594, (53, 892): 83.61013712882266, (53, 894): 83.85610645166634, (53, 896): 85.18966786365868, (53, 903): 83.81181081279168, (53, 909): 86.29302262427704, (53, 910): 86.3360529269719, (53, 912): 86.74869616448471, (53, 913): 87.08091740250035, (53, 916): 87.71784430059701, (53, 926): 86.54474309447735, (53, 927): 86.87036871446496, (53, 948): 84.73150133628803, (53, 961): 85.76720864089022, (53, 962): 85.92192430868224, (53, 963): 86.0194517711659, (53, 967): 83.64391288019388, (53, 974): 83.19302390555823, (53, 998): 83.04437917082738, (53, 1014): 72.80416684850067, (53, 1086): 97.1824806621232, (53, 1087): 98.5848426586808, (53, 1089): 98.51134521633271, (53, 1090): 98.1211009604881, (53, 1092): 97.15523229652545, (53, 1097): 97.63205152767414, (53, 1107): 97.51991109567237, (53, 1387): 217.03152107605894, (53, 1554): 227.21302357709374, (53, 1827): 45.62622603262144, (53, 1828): 45.78859475371532, (53, 1829): 45.55787043701165, (53, 1830): 44.61528358855938, (53, 1831): 44.7495359476915, (53, 1832): 44.90674495943396, (53, 1833): 45.076348726896995, (53, 1836): 45.33668765361774, (53, 1841): 44.73421830998996, (53, 1843): 44.87763800350039, (53, 1844): 44.63855586416601, (53, 1845): 44.656970763595034, (53, 1847): 45.735574760550485, (53, 1848): 45.4773338529002, (53, 1849): 44.108228578942985, (53, 1850): 44.14843076497726, (53, 1851): 44.81398504177991, (53, 1852): 44.39260816645156, (53, 1854): 44.58857892504883, (53, 1856): 45.239044906943356, (53, 1857): 45.27419077382416, (53, 1858): 44.50618336228108, (53, 1861): 45.222440705153225, (53, 1866): 44.90784472253453, (53, 1867): 45.068745638827494, (53, 1868): 45.51695556049662, (53, 1870): 44.13073936389636, (53, 1871): 45.43855827180862, (53, 1875): 44.87454113385262, (53, 1880): 45.44381127091456, (53, 1882): 44.79555800795596, (53, 1883): 44.60581035912287, (53, 1889): 45.99670079563034, (53, 1893): 46.21375487073938, (53, 1894): 46.47473572589744, (53, 1899): 46.404822703737445, (53, 1900): 46.43467665778345, (53, 1902): 45.96478196770583, (53, 1905): 45.512224531528794, (53, 1907): 45.741570329595, (53, 1910): 46.17426745647369, (53, 1917): 46.480047546428096, (53, 1920): 46.08551929272117, (53, 1935): 46.278649828628396, (53, 1937): 45.98920242330884, (53, 1946): 47.64834194001166, (53, 1949): 47.6888529841261, (53, 1950): 47.260394817780785, (53, 1951): 47.24022727658356, (53, 1952): 45.984619806049054, (53, 1953): 46.85827166844506, (53, 1954): 46.28397776297172, (53, 1958): 47.297103071794496, (53, 1960): 46.7580980164947, (53, 1968): 46.54828557644565, (53, 1969): 47.04607497504477, (53, 1974): 46.838056903090326, (53, 1975): 46.57199594190244, (53, 1979): 47.441674176256285, (53, 1980): 46.6723821885538, (53, 1981): 47.07235036811375, (53, 1985): 47.212233304062664, (53, 1994): 45.69693005261091, (53, 2011): 44.53498882009017, (53, 2019): 42.12000318348566, (53, 2020): 42.430231543835966, (53, 2029): 42.85157876226561, (53, 2030): 42.65828723355694, (53, 2032): 42.52927716359204, (53, 2033): 42.684470763249976, (53, 2034): 42.3017213373326, (53, 2036): 41.295880995778035, (53, 2037): 41.6070000392113, (53, 2038): 43.35569582776146, (53, 2042): 41.03757667386021, (53, 2050): 43.356134427611, (53, 2051): 42.971864814244476, (53, 2053): 43.09246794423559, (53, 2054): 42.86891196920639, (53, 2066): 43.251840473336934, (53, 2067): 43.46431278440492, (53, 2071): 46.312038599439944, (53, 2072): 46.22646491474567, (53, 2073): 48.33598565576445, (53, 2074): 48.13077732507813, (53, 2080): 48.15104890557118, (53, 2082): 46.091547571574786, (53, 2083): 46.07759875140787, (53, 2089): 46.76548842469637, (53, 2090): 46.82207506545793, (53, 2092): 47.285283624676424, (53, 2098): 48.41381005062186, (53, 2099): 47.95645085816379, (53, 2101): 48.10187643051052, (53, 2102): 47.560991831839274, (53, 2103): 47.58078079844074, (53, 2104): 47.42670422544654, (53, 2106): 45.79469553261152, (53, 2112): 47.69826486428105, (53, 2113): 47.26682271063677, (53, 2114): 46.52108732488847, (53, 2117): 45.398619957642914, (53, 2123): 60.807422310343235, (53, 2124): 60.738661835354755, (53, 2134): 59.9522647733498, (53, 2138): 60.13541298857598, (53, 2141): 60.229896091350305, (53, 2148): 56.300862092819635, (53, 2150): 60.23384215906115, (53, 2151): 59.87180828604245, (53, 2152): 60.01923239949701, (53, 2153): 56.63623489964147, (53, 2154): 57.22187323038976, (53, 2155): 56.62806240133819, (53, 2156): 57.15222538049627, (53, 2157): 54.74442019745953, (53, 2160): 58.18229608367123, (53, 2161): 59.65687696955522, (53, 2162): 55.180193248928674, (53, 2163): 55.42772415713781, (53, 2164): 55.20620734166827, (53, 2168): 58.253844491209875, (53, 2172): 56.44006452593214, (53, 2174): 59.40222116782019, (53, 2178): 55.86025754409344, (53, 2179): 55.77441234560441, (53, 2183): 59.69467080841352, (53, 2185): 59.45238675427159, (53, 2186): 59.635692659914014, (53, 2190): 58.58933423688541, (53, 2192): 58.83672649391482, (53, 2193): 59.80803723617935, (53, 2194): 60.05872387637795, (53, 2195): 59.586689046100965, (53, 2197): 58.533199633812146, (53, 2205): 58.17400403607179, (53, 2207): 57.88516414079866, (53, 2208): 57.943672268123734, (53, 2212): 60.857313818899144, (53, 2214): 57.91214999120002, (53, 2225): 55.9390830209893, (53, 2231): 67.1452098092949, (53, 2278): 50.16205198599542, (53, 2284): 48.82729217894266, (53, 2285): 48.59233709269254, (53, 2291): 47.71786821432949, (53, 2292): 50.036554126118595, (53, 2307): 49.13370323040454, (53, 2313): 47.11122731012346, (53, 2317): 51.47115580177968, (53, 2319): 49.5898050782388, (53, 2321): 48.90952695809385, (53, 2323): 49.645427118229186, (53, 2326): 49.97889951707695, (53, 2327): 50.22022525422898, (53, 2329): 50.31272844193886, (53, 2330): 50.252344656638265, (53, 2332): 49.51201469282, (53, 2344): 51.16484255450799, (53, 2346): 50.68068801055241, (53, 2361): 54.95268954003856, (53, 2368): 49.88154060817879, (53, 2374): 49.244485370695045, (53, 2375): 49.42791259110819, (53, 2377): 50.64925742982105, (53, 2378): 49.0557369205904, (53, 2379): 48.50736851605246, (53, 2380): 48.79952548976661, (53, 2383): 50.73692158790654, (53, 2385): 50.788109519242916, (53, 2395): 51.239057019709996, (53, 2397): 48.37032539895386, (53, 2398): 50.987786695160594, (53, 2399): 50.90453523414242, (53, 2400): 50.98738514189054, (53, 2402): 49.020144461709954, (53, 2403): 48.783542720609724, (53, 2404): 48.937424471815184, (53, 2405): 49.31646835768193, (53, 2407): 49.31747100167229, (53, 2408): 48.82065328904353, (53, 2409): 49.28147954756945, (53, 2411): 47.91710706652194, (53, 2412): 48.30458040567689, (53, 2413): 47.99105843226013, (53, 2414): 48.19019399390196, (53, 2422): 47.68765672007303, (53, 2424): 48.42814670356671, (53, 2426): 48.5540146853087, (53, 2433): 48.65027549778761, (53, 2436): 48.20277403596074, (53, 2437): 49.77162658043709, (53, 2440): 49.57271539288806, (53, 2445): 39.07628566529564, (53, 2447): 40.22955169830803, (53, 2454): 39.64310972533932, (53, 2455): 40.04490325624516, (53, 2460): 41.36373660353297, (53, 2461): 41.09481851301451, (53, 2471): 35.19411248700278, (53, 2492): 23.73690187779191, (53, 2511): 28.755141777610532, (53, 2523): 26.140757021490774, (53, 2525): 25.845736729850064, (53, 2535): 32.720248071573394, (53, 2537): 32.986370299476896, (53, 2538): 33.1887790210679, (53, 2539): 31.442529707740597, (53, 2540): 32.5559159054563, (53, 2542): 31.699928532436168, (53, 2559): 31.488025690156555, (53, 2575): 29.107904685511876, (53, 2599): 42.64392612558793, (53, 2600): 39.2101554684866, (53, 2607): 42.666555693048764, (53, 2627): 21.417790557663015, (53, 2647): 18.657696783285477, (53, 2674): 21.148680171910986, (53, 2681): 20.621154847734882, (53, 2683): 20.10822156685638, (53, 2686): 21.46589361752548, (53, 2689): 12.5, (53, 2690): 12.5, (53, 2713): 12.5, (53, 2714): 12.5, (53, 2715): 12.5, (53, 2739): 12.5, (53, 2740): 12.5, (53, 2741): 12.5, (53, 2749): 12.5, (53, 2750): 12.5, (53, 2752): 12.5, (53, 2755): 12.5, (53, 2758): 12.5, (53, 2759): 12.5, (53, 2769): 12.5, (53, 2771): 12.5, (53, 2779): 12.5, (53, 2784): 12.5, (53, 2800): 12.5, (53, 2802): 12.5, (53, 2803): 12.5, (53, 2804): 12.5, (53, 2805): 12.5, (53, 2807): 12.5, (53, 2809): 12.5, (53, 2812): 12.5, (53, 2814): 12.5, (53, 2817): 12.5, (53, 2819): 12.5, (53, 2823): 12.5, (53, 2832): 12.5, (53, 2836): 12.5, (53, 2839): 12.5, (53, 2841): 12.5, (53, 2843): 12.5, (53, 2846): 12.5, (53, 2849): 12.5, (53, 2852): 12.5, (53, 2853): 12.5, (53, 2876): 12.5, (53, 2877): 12.5, (53, 2885): 12.5, (53, 2918): 12.5, (53, 2921): 12.5, (53, 2925): 12.5, (53, 2926): 12.5, (53, 2930): 12.5, (53, 2931): 12.5, (53, 2938): 12.5, (53, 2940): 12.5, (53, 2947): 12.5, (53, 2949): 12.5, (53, 2950): 12.5, (53, 2952): 12.5, (53, 2958): 12.5, (53, 2959): 12.5, (53, 2960): 12.5, (53, 2961): 12.5, (53, 2963): 12.5, (53, 2968): 12.5, (53, 2976): 12.5, (53, 2981): 12.5, (53, 2982): 12.5, (53, 2984): 12.5, (53, 3003): 12.5, (53, 3046): 14.464586421197934, (53, 3050): 12.5, (53, 3051): 12.5, (53, 3053): 12.5, (53, 3069): 12.5, (53, 3071): 12.5, (53, 3080): 12.5, (53, 3199): 12.5, (53, 3200): 12.5, (53, 3205): 12.5, (53, 3209): 12.5, (53, 3215): 12.5, (53, 3217): 12.5, (53, 3249): 12.5, (53, 3263): 12.5, (53, 3289): 12.5, (53, 3301): 12.5, (53, 3302): 12.5, (53, 3307): 12.5, (53, 3310): 12.5, (53, 3391): 25.79284687084741, (53, 3509): 123.71193538995173, (53, 3510): 124.22208969781724, (53, 3511): 123.92110616318001, (53, 3512): 124.27215314234743, (53, 3514): 124.1985226357648, (53, 3519): 122.35336885399501, (53, 3536): 122.88211756772877, (53, 3545): 122.12545562294702, (53, 3548): 122.96591287282273, (53, 3572): 122.5434238164544, (53, 3581): 123.04233419614279, (53, 3583): 123.53967532032337, (53, 3601): 121.35292716571712, (53, 3656): 122.10078581247161, (53, 3669): 123.02441807739007, (53, 3670): 122.56622151870171, (53, 3695): 125.19656212588806, (53, 3696): 124.83561892088294, (53, 3782): 123.8944845553235, (53, 3792): 124.2405194010096, (53, 3989): 338.1788105469486, (53, 4008): 340.6804523324973, (53, 4031): 340.0624459856209, (53, 4045): 339.60886864432376, (53, 4144): 340.1653871156574, (53, 4145): 338.09609213365155, (53, 4164): 339.30402299959604, (53, 4168): 338.73131191321573, (53, 4173): 338.67521766413586, (53, 4181): 337.1432593594211, (53, 4228): 335.22672528947953, (53, 4248): 335.2293406913592, (53, 4254): 323.18180651623385, (53, 4260): 323.06058933919115, (53, 4262): 324.0668669892709, (53, 4273): 323.761173194541, (53, 4319): 316.10885980797565, (53, 4326): 315.7940791538425, (53, 4328): 315.86472163074006, (53, 4334): 316.5091933801827, (53, 4335): 316.3317753090925, (53, 4372): 307.25472824855666, (53, 4413): 315.0346735868643, (53, 4434): 307.02582869754804, (53, 4447): 308.4474983208958, (53, 4452): 307.08548645078304, (53, 4463): 287.97046571705545, (53, 4465): 288.6893893491207, (53, 4619): 314.7818672487879, (53, 4645): 316.8972353926, (53, 4657): 316.4350462135078, (53, 4666): 315.54507787111055, (53, 4676): 316.89206387889635, (53, 4678): 317.2686595943328, (53, 4689): 316.1593644749307, (53, 4704): 322.8181178045276, (53, 4726): 335.1141758419392, (53, 4727): 334.87161830389323, (53, 4730): 334.4151082238359, (53, 4731): 334.454016085522, (53, 4734): 335.2444106648534, (53, 4735): 334.93547438559295, (53, 4736): 334.98308618537027, (53, 4737): 334.48157395708955, (53, 4738): 334.4806480382857, (53, 4756): 334.6812311385783, (53, 4760): 333.8483997135534, (53, 4761): 334.14046616150443, (53, 4762): 333.42210649377023, (53, 4765): 333.9218713375704, (53, 4773): 335.6691113930219, (53, 4774): 335.31693202276404, (53, 4790): 335.5281638034377, (53, 4795): 335.35007910334105, (53, 4799): 335.3498803552347, (53, 4801): 335.671504732192, (53, 4804): 335.6018345746727, (53, 4805): 335.453335093356, (53, 4806): 335.0244370426182, (53, 4815): 334.67229476473904, (53, 4816): 335.34169007106476, (53, 4817): 335.30471012260796, (53, 4826): 334.99138914742355, (53, 4830): 334.5799498275099, (53, 4839): 334.5489686813275, (53, 4840): 334.69979100080127, (53, 4841): 334.1339065881748, (53, 4846): 333.99146296340933, (53, 4848): 333.8031977487803, (53, 4850): 334.0013062873802, (53, 4871): 331.78412630040157, (53, 4883): 333.7671513158151, (53, 4900): 332.93232454657385, (53, 4901): 332.5246215691296, (53, 4917): 312.1456494113747, (53, 4931): 310.2120493834776, (53, 4944): 312.4647200859867, (53, 4956): 310.4670100598244, (53, 4958): 310.213620982614, (53, 4959): 309.71112862276703, (53, 4961): 310.9390982010786, (53, 4966): 309.8801240828713, (53, 5207): 307.71732794782616, (53, 5272): 276.5873295511244, (53, 5283): 277.2421257079203, (53, 5287): 277.8867837995955, (53, 5289): 278.15847779484466, (53, 5293): 277.0951186396912, (53, 5295): 278.98605871977924, (53, 5296): 278.73032748390614, (53, 5298): 278.57240207145543, (53, 5303): 278.9214219896029, (53, 5305): 275.7256180715861, (53, 5306): 274.85604634757834, (53, 5307): 275.35599076003695, (53, 5308): 275.9550830093352, (53, 5313): 276.2342984556764, (53, 5314): 276.75049615533095, (53, 5317): 275.7994525665495, (53, 5319): 278.2126059074079, (53, 5324): 278.01832543203705, (53, 5326): 277.90710471918834, (53, 5348): 274.4886672396874, (53, 5351): 274.63953127375436, (53, 5399): 278.1797420041533, (53, 5413): 274.9444394241095, (53, 5422): 278.7888332956009, (53, 5445): 277.13708915254176, (53, 5448): 276.4902758083434, (53, 5456): 276.0777303216605, (53, 5467): 276.6090475158026, (53, 5624): 270.3271855312991, (53, 5671): 294.64965914670614, (53, 5672): 293.78672780775304, (53, 5797): 305.10527184273985, (53, 5871): 284.89619004436577, (53, 5976): 277.1583103670361, (53, 6118): 68.2616775023599, (53, 6248): 66.3112776823458, (53, 6345): 238.1655200677906, (53, 6352): 235.78897324457526, (53, 6354): 238.7396601993215, (53, 6359): 239.2220590458684, (53, 6376): 236.20371560774169, (53, 6378): 238.4591211248568, (53, 6381): 239.03698683845406, (53, 6383): 237.65590399219082, (53, 6396): 238.83082680094898, (53, 6399): 238.2122412055735, (53, 6408): 235.86062112005115, (53, 6409): 236.9484997348517, (53, 6419): 233.0631391479428, (53, 6422): 236.1468115428182, (53, 6423): 235.95305603076193, (53, 6424): 238.47507951724035, (53, 6439): 238.01091864910953, (53, 6464): 237.34447805771472, (53, 6465): 237.11367514409667, (53, 6469): 237.42897758789164, (53, 6470): 237.28792423631722, (53, 6472): 240.03282398309318, (53, 6480): 239.49601911416133, (53, 6486): 240.9018279830285, (53, 6497): 240.42611746350892, (53, 6503): 237.4914551952826, (53, 6508): 237.66030727130425, (53, 6509): 238.12194859817956, (53, 6521): 239.78459673667254, (53, 6544): 239.61873938253393, (53, 6552): 236.52600776685497, (53, 6553): 236.15420204438718, (53, 6554): 235.77597836557396, (53, 6578): 237.1483090124252, (53, 6582): 236.87063045040892, (53, 6601): 237.31734860441136, (53, 6609): 240.31607845376982, (53, 6610): 240.42024715919638, (53, 6611): 240.49931396227123, (53, 6614): 240.3096941599551, (53, 6615): 240.37578185381358, (53, 6616): 240.7574238099312, (53, 6617): 240.5888724049024, (53, 6618): 241.1344123166664, (53, 6619): 240.03726192584298, (53, 6620): 240.76366371459716, (53, 6621): 240.44600893479404, (53, 6622): 240.52131626288102, (53, 6623): 240.2707924500906, (53, 6624): 239.9844718999641, (53, 6625): 239.9265775007996, (53, 6626): 240.02167085125916, (53, 6627): 240.23631103431273, (53, 6628): 240.6970293111745, (53, 6629): 240.0698462995265, (53, 6630): 239.66023594205623, (53, 6632): 240.0384052354937, (53, 6634): 239.31400002820692, (53, 6635): 240.33264047259823, (53, 6636): 240.77454878162416, (53, 6637): 239.63351419183275, (53, 6638): 239.69471248857795, (53, 6639): 240.26590798519032, (53, 6640): 239.75035235121874, (53, 6641): 240.43727652183964, (53, 6642): 239.69958659232694, (53, 6643): 239.98957246249037, (53, 6645): 240.0796810652083, (53, 6646): 241.02119732996982, (53, 6647): 239.79666776524206, (53, 6653): 240.36281500872298, (53, 6655): 240.27130176905516, (53, 6658): 239.28875054994518, (53, 6662): 239.67905246644068, (53, 6819): 221.53514290781968, (53, 6996): 227.9918517606547, (53, 7059): 232.2449759454671, (53, 7187): 226.40278698163627, (53, 7304): 216.38086248847756, (53, 7528): 228.13245856110487, (53, 7720): 252.96599615821862, (53, 7793): 252.64373279707723, (53, 7807): 252.92344138711584, (53, 7808): 252.56710867175667, (53, 7831): 242.64050130035568, (53, 7850): 246.67199938340454, (53, 7852): 245.74285864507414, (53, 8012): 251.5270244571525, (53, 8125): 256.59475106839596, (53, 8208): 260.80445882564885, (53, 8392): 245.9660602540274, (53, 8651): 201.08192570141892, (53, 9088): 220.11144711928705, (53, 9443): 193.18041747248074, (53, 9444): 193.8354889714038, (53, 9828): 176.52469952991936, (53, 9868): 174.1438729375748, (53, 10180): 257.12056954622204, (53, 10256): 268.1163904839356, (53, 10276): 262.8552419005232, (53, 10378): 263.6478794955743, (53, 10676): 254.51935984929005, (53, 10714): 247.67823797497837, (53, 10730): 248.157728190484, (53, 10862): 248.15554265368553, (53, 10881): 249.84880552617315, (53, 10883): 249.61934091207252, (53, 10885): 247.8020662075504, (53, 10891): 249.26444135593468, (53, 10909): 249.2151299814937, (53, 10911): 249.55482450840046, (53, 10913): 249.1310345871408, (53, 10915): 249.166165576941, (53, 10919): 249.44605152732217, (53, 11037): 236.84756985673943, (53, 11039): 232.99174594903477, (53, 11516): 359.95562938609953, (53, 11856): 316.77153471977635, (53, 11857): 316.4911797066623, (53, 11861): 316.64893122122186, (53, 11881): 316.04272197846996, (53, 11902): 314.1782439672223, (53, 11911): 313.72385587380666, (53, 11914): 314.0341097941863, (53, 11922): 315.4600577479563, (53, 11924): 315.86952389309386, (53, 11926): 315.32557531107733, (53, 11950): 316.2549567049278, (53, 11963): 318.0280289333146, (53, 11983): 316.6044226623267, (53, 11985): 318.928746703447, (53, 12009): 318.3876594015122, (53, 12010): 317.1796445887416, (53, 12018): 317.35983985377334, (53, 12020): 317.72958501470913, (53, 12021): 317.91580784482943, (53, 12024): 319.116271108432, (53, 12025): 318.7509703308, (53, 12027): 318.45672981225283, (53, 12031): 316.9706914973032, (53, 12032): 317.41969573427855, (53, 12035): 318.2613809007155, (53, 12041): 319.1921991020707, (53, 12045): 302.3183133456094, (53, 12145): 309.79143630492206, (53, 12275): 338.38795290867785, (53, 12294): 334.8428732609395, (53, 12358): 344.4686224992346, (53, 12463): 347.98773784265313, (53, 12465): 347.85353368406294, (53, 12482): 349.8296373664533, (53, 12503): 349.523489931685, (53, 12506): 349.99122671953955, (53, 12549): 349.3089087241882, (53, 12559): 348.88653326425487, (53, 12569): 349.1530481770131, (53, 12572): 349.5115175966429, (53, 12574): 348.7988252541048, (53, 12576): 349.75508652030646, (53, 12591): 349.85815879708287, (53, 12608): 352.8418439275101, (53, 12696): 348.4012453092798, (53, 12710): 351.3117003477598, (53, 12728): 349.75030736076775, (53, 12766): 274.0510566626414, (53, 12771): 271.2875251966181, (53, 12790): 270.812619803633, (53, 12795): 269.6446501299338, (53, 12797): 265.6965118916349, (53, 12798): 266.3123583639464, (53, 12811): 269.71604502791865, (53, 12830): 268.458329549987, (53, 12848): 269.28899894290106, (53, 12850): 269.718653277033, (53, 12852): 268.36683100486954, (53, 12854): 267.8422485379604, (53, 12859): 269.87305712345676, (53, 12861): 266.9456424470735, (53, 12865): 270.25652234274, (53, 12866): 270.05571620337844, (53, 12867): 271.0446613518011, (53, 12874): 270.55526671286594, (53, 12875): 270.9819433966433, (53, 12881): 269.27438560585495, (53, 12883): 269.93148074639515, (53, 12885): 271.31087623685397, (53, 12888): 269.67610130844855, (53, 12889): 269.57460788803695, (53, 12892): 270.6413582682654, (53, 12893): 269.65258116153166, (53, 12896): 270.01357599464296, (53, 12906): 270.3816217216833, (53, 13018): 264.4947446386307, (53, 13071): 264.3073202871487, (53, 13131): 261.05229423915017, (53, 13146): 264.74605462353026, (53, 13159): 258.6782141100653, (53, 13193): 260.4486195811986, (53, 13198): 254.74825698999314, (53, 13292): 261.89908107138353, (53, 13296): 264.35812342412993, (53, 13406): 250.25895338368198, (53, 13407): 250.00700351247136, (53, 13417): 249.15250152538295, (53, 13418): 249.75434638336037, (53, 13438): 252.75035790652498, (53, 13442): 253.41597246059112, (53, 13443): 252.88079671830232, (53, 13764): 205.7159933917887, (53, 13766): 206.3941837913992, (53, 13771): 205.70454266555672, (53, 13783): 205.20557880662093, (53, 13784): 207.14716262227188, (53, 13792): 204.36424402001694, (53, 13824): 204.7326802155124, (53, 14017): 209.0165202867092, (53, 14870): 250.23042908322122, (53, 14997): 223.43271214437067, (53, 15000): 223.64051229602774, (53, 15003): 224.23795060223648, (53, 15006): 224.63772985619687, (53, 15007): 225.11124203857278, (53, 15056): 225.46903875820365, (53, 15063): 225.1425132120883, (53, 15069): 225.15304542162875, (53, 15076): 225.28104954818414, (53, 15086): 223.66375127469908, (53, 15087): 223.3590006041875, (53, 15111): 221.8429041097115, (53, 15116): 222.7271339889012, (53, 15722): 210.44994406587443, (53, 15998): 206.2502279227321, (53, 16073): 116.78374039231613, (53, 16939): 54.93653043400478, (53, 16940): 55.618216129063285, (53, 16951): 54.019598643745894, (53, 16963): 54.15426526511101, (53, 16965): 53.68543665309279, (53, 16969): 53.369438428916254, (53, 16970): 54.143649771019774, (53, 16971): 54.59834490766368, (53, 16973): 54.338704607793474, (53, 16974): 53.21131959801444, (53, 16976): 54.29859455840645, (53, 16978): 54.731341583480635, (53, 16980): 54.393488987992335, (53, 16982): 52.90458805153974, (53, 17045): 24.137278200718743, (53, 17048): 23.300026570668518, (53, 17304): 332.0855548999916, (53, 17305): 331.39835247091537, (53, 17330): 331.9021102089643, (53, 17334): 331.2458065149977, (53, 17343): 332.51554117672964, (53, 17345): 330.96771968677865, (53, 17347): 331.6797962156733, (53, 17351): 330.04879071731756, (53, 17372): 331.0548323635577, (53, 17373): 332.5014325851218, (53, 17377): 332.5827642753916, (53, 17382): 331.5888524941606, (53, 17383): 331.85614894349624, (53, 17389): 331.24946820774517, (53, 17400): 332.3018614153799, (53, 17401): 332.3210020952958, (53, 17402): 332.33694840829526, (53, 17403): 332.4161184202294, (53, 17440): 330.7594249635241, (53, 17455): 332.1780317749282, (53, 17491): 332.0884450948743, (53, 17507): 331.20538722841036, (53, 17509): 331.8296889418429, (53, 17590): 329.3977994327545, (53, 17615): 327.8043998095128, (53, 17642): 328.25389319486754, (53, 17643): 328.11465329982997, (53, 17668): 327.8375589534551, (53, 17721): 327.00127178808503, (53, 17754): 332.4884083693021, (53, 17769): 331.6636093501891, (53, 17776): 328.9773165505004, (53, 17804): 332.6254474201325, (53, 17809): 333.1949056137746, (53, 17824): 332.97317970239334, (53, 17837): 330.6143449972925, (53, 17838): 330.53853416412704, (53, 17862): 330.0496707817896, (53, 17866): 331.3254327038904, (53, 17872): 329.725325955827, (53, 17873): 328.71974447812903, (53, 17881): 330.2421311739819, (53, 17947): 115.87873643298303, (53, 17951): 116.49577658649987, (53, 17953): 116.87562825379375, (53, 17954): 117.00325935001459, (53, 17959): 115.55187782404754, (53, 17963): 115.32284087569407, (53, 18000): 119.4481147339629, (53, 18001): 119.61923781444376, (53, 18111): 124.342486294, (53, 18148): 141.8093129879476, (53, 18166): 135.97125355105055, (53, 18189): 127.8678319158215, (53, 18239): 332.88345675820597, (53, 18240): 332.84560736099473, (53, 18245): 332.9205047372012, (53, 18247): 332.7630208829271, (53, 18251): 332.8805045775824, (53, 18256): 332.97154550647224, (53, 18258): 332.8109365880523, (53, 18259): 332.8198087948863, (53, 18260): 332.8516379465035, (53, 18262): 332.93514785090343, (53, 18263): 332.99118315951796, (53, 18264): 333.02484826143825, (53, 18266): 332.94954666619947, (53, 18267): 332.98684875319964, (53, 18268): 332.9934739478758, (53, 18269): 333.0644259763822, (53, 18275): 333.03081478852613, (53, 18285): 333.025718945302, (53, 18308): 332.2727920508166, (53, 18313): 331.92978909490853, (53, 18314): 331.9901700607847, (53, 18315): 333.1475134308843, (53, 18316): 333.09859584303695, (53, 18317): 333.1291449017102, (53, 18320): 333.2187756219046, (53, 18321): 333.2166092580952, (53, 18322): 333.2732899435205, (53, 18324): 333.3794553012983, (53, 18325): 333.6141844591456, (53, 18326): 333.52866569074826, (53, 18327): 333.12191274733556, (53, 18329): 333.7665240058728, (53, 18330): 333.5183639606153, (53, 18331): 333.3819963964863, (53, 18332): 333.21979506236784, (53, 18333): 333.53133264044584, (53, 18336): 333.46245378832964, (53, 18337): 333.56899081236935, (53, 18403): 333.21357642078755, (53, 18432): 328.7743940748765, (53, 18451): 331.77882970990834, (53, 18466): 334.807159123095, (53, 18481): 333.3192239483966, (53, 18483): 333.28981930372527, (53, 18484): 333.18307754262156, (53, 18485): 332.89097634718985, (53, 18486): 333.3409398128187, (53, 18487): 333.0751404867479, (53, 18489): 333.20669467170615, (53, 18490): 333.5854310084331, (53, 18491): 333.7270568735845, (53, 18492): 332.74835033061856, (53, 18493): 333.32499769845583, (53, 18494): 333.1256586444388, (53, 18495): 333.4842297031706, (53, 18496): 333.3120591335779, (53, 18497): 333.0404905820227, (53, 18498): 332.99234353299073, (53, 18499): 333.2020422203664, (53, 18501): 333.1012356802027, (53, 18502): 332.97032326599583, (53, 18503): 332.83482124230545, (53, 18504): 333.33499843116573, (53, 18506): 333.203889395231, (53, 18507): 333.0952658927569, (53, 18508): 333.2008418511329, (53, 18509): 333.2308661092971, (53, 18510): 332.87844480739176, (53, 18511): 333.4241142334609, (53, 18512): 333.2107925991102, (53, 18515): 333.3887597384771, (53, 18516): 333.4939601410901, (53, 18517): 333.36955894458185, (53, 18518): 333.5798289011549, (53, 18519): 333.3474026817008, (53, 18520): 333.12662552431163, (53, 18522): 333.86423911017096, (53, 18523): 333.92573962429816, (53, 18532): 334.16084728561594, (53, 18535): 333.7047933143709, (53, 18537): 333.4508877995407, (53, 18539): 333.5204154321053, (53, 18540): 333.56732992461383, (53, 18541): 333.70664162798255, (53, 18542): 333.7920980510062, (53, 18543): 333.38039620912315, (53, 18546): 333.6291673688251, (53, 18555): 334.030060527095, (53, 18556): 334.12425897068096, (53, 18565): 334.173485856878, (53, 18567): 334.35183163658036, (53, 18568): 334.10708795993776, (53, 18577): 335.66173792158673, (53, 18583): 335.315243099857, (53, 18605): 335.53896160301315, (53, 18608): 334.6096391021928, (53, 18616): 336.99697862953394, (53, 18618): 338.2919914767966, (53, 18625): 337.64061031970186, (53, 18645): 336.451319467775, (53, 18646): 336.8124291576666, (53, 18653): 335.99595629852644, (53, 18654): 337.0023720236263, (53, 18655): 336.3874262822106, (53, 18666): 340.03325114386894, (53, 18837): 332.10507768536297, (53, 18974): 331.0184280504262, (53, 18999): 331.6619151744617, (53, 19000): 332.0274112548732, (53, 19174): 312.6612818886467, (53, 19342): 319.4610086634556, (53, 19455): 316.8139338106854, (53, 19555): 298.02329189624896, (53, 19564): 298.4695187892276, (53, 19573): 297.8291695155284, (53, 19586): 297.58405413229764, (53, 19605): 297.97413605999276, (53, 19611): 298.431195326136, (53, 19614): 298.3936982843188, (53, 19641): 306.8052655008434, (53, 19702): 306.4608934129323, (53, 19713): 305.88587423767007, (53, 19731): 295.9650187516573, (53, 19819): 313.65135202324467, (53, 19893): 299.8449668817343, (53, 19899): 303.8958913705498, (53, 19929): 300.91873056706424, (53, 19951): 309.0200959369184, (53, 19962): 301.5626383477549, (53, 19970): 303.3812783585796, (53, 19971): 303.4106610452237, (53, 19972): 302.7211389425325, (53, 19975): 302.4052169852672, (53, 19978): 310.80042482452717, (53, 19987): 310.9502004816949, (53, 19989): 308.7143942678598, (53, 20039): 311.36644149873666, (53, 20043): 312.3154997123506, (53, 20047): 311.6126164620305, (53, 20052): 309.1263552672455, (53, 20054): 309.31494221855587, (53, 20085): 320.6431338508916, (53, 20104): 321.34874980137846, (53, 20132): 317.0122666181887, (53, 20203): 299.27938616653034, (53, 20280): 298.30395642150245, (53, 20285): 298.044494449418, (53, 20290): 298.70738394799355, (53, 20297): 297.9542604248788, (53, 20309): 311.24104955516765, (53, 20453): 323.02378678379415, (53, 20485): 293.2059662214539, (53, 20520): 291.29590278748236, (53, 20526): 290.5146013197411, (53, 20698): 187.00308686919584, (53, 20868): 163.93058035001886, (53, 21042): 272.480398352479, (53, 21057): 277.12895099335077, (53, 21066): 274.96386972847614, (53, 21075): 273.92547660574223, (53, 21093): 272.98914888784, (53, 21098): 276.5219384989553, (53, 21127): 272.94758309854006, (53, 21130): 273.902949699653, (53, 21144): 273.6213086039546, (53, 21146): 272.6427869964942, (53, 21147): 273.4986414782189, (53, 21148): 274.35921708227164, (53, 21153): 271.84565247311076, (53, 21293): 280.39535391589175, (53, 21426): 277.7505168016275, (53, 21442): 282.4259251429141, (53, 21451): 282.8836186155502, (53, 21466): 280.1555684399235, (53, 21469): 280.9222029525231, (53, 21471): 279.76349964893376, (53, 21473): 280.41556922245684, (53, 21475): 279.85255553692866, (53, 21482): 281.3452578483045, (53, 21484): 281.21791706339, (53, 21488): 280.751735694658, (53, 21494): 279.93275659361586, (53, 21498): 280.48241878795767, (53, 21500): 279.67939537861145, (53, 21514): 281.4961830268888, (53, 21537): 279.70776664224775, (53, 21662): 282.38465680992175, (53, 21691): 279.4504699013353, (53, 21757): 273.5922512687452, (53, 21777): 263.97987996236895, (53, 21778): 263.24153548899955, (53, 21779): 263.7246072927142, (53, 21790): 264.7347535274453, (53, 21802): 264.83385979592845, (53, 21824): 265.6709589685271, (53, 21874): 264.002650923753, (53, 21879): 263.69658853123184, (53, 21983): 266.0969541587656, (53, 22002): 274.53408017948544, (53, 22132): 267.85706015424796, (53, 22261): 178.17695808320792, (53, 22298): 180.24448692517325, (53, 22339): 175.09522401338845, (53, 22508): 190.66608355131436, (53, 22841): 69.39907902895072, (53, 22842): 69.00558067553948, (53, 22874): 67.76348689094301, (53, 22941): 69.08417402040656, (53, 22956): 68.68134113599018, (53, 22960): 69.60897640390158, (53, 22968): 64.17123720417128, (53, 22970): 64.93694249111603, (53, 22974): 61.50671465393869, (53, 22980): 61.426574304350176, (53, 23025): 56.50002953831305, (53, 23028): 55.50048147707922, (53, 23081): 49.20914517431343, (53, 23104): 40.9281087616383, (53, 23147): 57.13730563407202, (53, 23298): 294.7613231046797, (53, 23376): 292.67614128582676, (53, 23381): 291.79922076337795, (53, 23529): 296.39714150242145, (53, 23556): 295.1434849699141, (53, 23718): 293.1676205728398, (53, 24001): 307.02860011264937, (53, 24094): 311.54567985210576, (53, 24129): 313.61833876974646, (53, 24174): 309.57717846243844, (53, 24235): 314.3585295973277, (53, 24259): 316.16509082927547, (53, 24260): 316.04334115127364, (53, 24261): 315.5731278187992, (53, 24305): 318.45708929030775, (53, 24306): 318.89397570870676, (53, 24307): 318.2688890258269, (53, 24308): 311.7167023968695, (53, 24498): 323.13324662892256, (53, 24499): 323.1922495793797, (53, 24500): 322.79439511142783, (53, 24668): 319.4531188388303, (53, 24711): 326.0509139199391, (53, 24756): 327.7293329114585, (53, 24788): 328.20239475178954, (53, 24809): 326.18666101906797, (53, 24813): 326.789914301014, (53, 24821): 326.57956598328144, (53, 24825): 326.7883719980258, (53, 24832): 326.00779538689727, (53, 24833): 326.3459566375504, (53, 24835): 326.6988829387334, (53, 24837): 327.198961862444, (53, 24840): 325.9749291261826, (53, 24841): 326.4570142683032, (53, 24844): 326.0167506357047, (53, 24845): 326.2214065202366, (53, 24846): 326.33762098326554, (53, 24849): 326.53463701600754, (53, 24850): 326.92555090539673, (53, 24863): 322.0314573907029, (53, 24866): 322.62602070086, (53, 24885): 323.4308004610695, (53, 24886): 323.5407087344781, (53, 24889): 324.65524007442957, (53, 24903): 325.0739859247203, (53, 24909): 322.7321667700904, (53, 24999): 347.930714419562, (53, 25019): 346.9821462564622, (53, 25028): 347.63795421805725, (53, 25137): 299.63546405265095, (53, 25145): 300.4605438338381, (53, 25208): 309.7779943044838, (53, 25233): 308.6524291689582, (53, 25371): 299.7699412249238, (53, 25377): 297.43917258714384, (53, 25828): 255.3094342364562, (53, 25851): 248.8081795376811, (53, 25874): 254.9172175389168, (53, 25898): 257.7707169991029, (53, 25946): 254.64941765071757, (53, 26047): 268.2192520406688, (53, 26066): 282.8022478436737, (53, 26197): 273.33348906012986, (53, 26212): 235.40277758043018, (53, 26253): 233.43260940374142, (53, 26254): 234.13222465044348, (53, 26257): 234.98457955912343, (53, 26258): 233.87578458665854, (53, 26260): 234.43360251560335, (53, 26266): 233.30697425710156, (53, 26267): 234.0262581643702, (53, 26271): 234.09514808060328, (53, 26304): 240.9235212364412, (53, 26305): 240.74814608419948, (53, 26363): 253.39623990279176, (53, 26441): 190.8348329555969, (53, 26442): 190.7287959679152, (53, 26450): 191.62265616674074, (53, 26459): 192.8437495001476, (53, 26462): 193.23372168431032, (53, 26467): 190.86267973901457, (53, 26471): 190.9298711056211, (53, 26472): 190.827129298509, (53, 26473): 190.68718623506018, (53, 26476): 189.36156850044526, (53, 26485): 191.85961004341294, (53, 26493): 191.24018837588892, (53, 26524): 193.3968360106946, (53, 26525): 193.17067543211192, (53, 26556): 191.30840626658588, (53, 26560): 192.36689813729294, (53, 26561): 193.10549518791643, (53, 26564): 191.26225328523273, (53, 26569): 192.907172903599, (53, 26570): 192.73974761343055, (53, 26573): 192.08874572908798, (53, 26581): 191.64649295322016, (53, 26583): 192.11145870592787, (53, 26593): 191.05893993720042, (53, 26837): 190.22429071257486, (53, 26844): 189.9059310238049, (53, 26863): 189.46727551278917, (53, 26893): 188.05511696181074, (53, 26902): 187.57670910282587, (53, 26905): 189.090584522442, (53, 26912): 188.39342403244092, (53, 26921): 188.85924497532494, (53, 26922): 188.25416769463914, (53, 27212): 212.88458061176925, (53, 27218): 214.348688841789, (53, 27239): 212.10822335251555, (53, 27257): 211.98827575455175, (53, 27274): 211.77386202389974, (53, 27279): 211.39192431453756, (53, 27282): 211.735610366747, (53, 27283): 212.45173699176013, (53, 27285): 211.35645119516505, (53, 27286): 210.9030030223948, (53, 27290): 211.9600209855173, (53, 27295): 212.82421447169716, (53, 27300): 211.88925965953044, (53, 27344): 210.8428255801007, (53, 27366): 210.01659921649613, (53, 27383): 210.40358060325164, (53, 27398): 211.06724373926843, (53, 27406): 211.72335545593273, (53, 27407): 211.97848255023408, (53, 27426): 215.4055315693548, (53, 27432): 215.92495219751356, (53, 27460): 215.99393058430257, (53, 27523): 203.1432503975176, (53, 27545): 205.05017667594242, (53, 27602): 195.21932438094476, (53, 27606): 195.71007123178438, (53, 27646): 194.48892026594697, (53, 27667): 192.50152306496454, (53, 27672): 192.74738342295518, (53, 27674): 192.86543436205133, (53, 27688): 193.96117223901575, (53, 27692): 192.00930928075928, (53, 27693): 192.22980888980547, (53, 27705): 191.8488766397669, (53, 27712): 191.40474296756818, (53, 27786): 210.08293138024752, (53, 27790): 215.87815574808974, (53, 27791): 216.67685238890257, (53, 27795): 209.93813641987762, (53, 27801): 213.78128477825112, (53, 27813): 209.31805841235567, (53, 27816): 210.55669502597286, (53, 27823): 213.9730245781345, (53, 27830): 211.99273859586083, (53, 27884): 194.0631546169295, (53, 27885): 194.73375081219746, (53, 27896): 194.49942392157467, (53, 27919): 194.8477325531919, (53, 27922): 194.38662867349413, (53, 27930): 194.61549298726317, (53, 27934): 194.31350482634497, (53, 27935): 193.95873686246856, (53, 27948): 176.97678134567047, (53, 27951): 182.68575805527124, (53, 28061): 149.48453467292344, (53, 28290): 130.1131521322464, (53, 28292): 128.14957799690825, (53, 28293): 129.60293311711797, (53, 28295): 128.74635850566222, (53, 28296): 129.58871041680504, (53, 28297): 131.04428592280692, (53, 28302): 130.2580149902837, (53, 28310): 78.00337010559647, (53, 28313): 77.81335533708868, (53, 28372): 76.85128386875111, (53, 28398): 76.8329976852674, (53, 28399): 77.16344785504387, (53, 28400): 76.72098880924094, (53, 28401): 77.79779701584687, (53, 28445): 78.54891921925586, (53, 28475): 78.33104512306136, (53, 28885): 314.76840514771243, (53, 28886): 314.3794859857729, (53, 28915): 314.75325923381195, (53, 28916): 314.4076352022845, (53, 28917): 314.19887713492295, (53, 28921): 315.49999937899634, (53, 28931): 315.40129904923714, (53, 28945): 313.5306658245122, (53, 28982): 313.98263744831985, (53, 29219): 316.3587124511909, (53, 29228): 314.56887837815157, (53, 29246): 326.1974756723336, (53, 29248): 326.03933872464125, (53, 29282): 323.62839971563915, (53, 29290): 327.3729164255936, (53, 29291): 326.89160692201614, (53, 29292): 327.34335869619235, (53, 29293): 326.40052054241454, (53, 29294): 327.15328058655564, (53, 29298): 326.47369433352225, (53, 29299): 326.39465392083173, (53, 29304): 325.50978733943793, (53, 29317): 323.2433888184171, (53, 29323): 323.0670397732578, (53, 29330): 324.1596206246385, (53, 29331): 324.700152957046, (53, 29344): 316.5852646665781, (53, 29445): 296.1082754218825, (53, 29724): 85.41175101394764, (53, 29738): 85.3605954978952, (53, 29745): 86.10605266064717, (53, 29748): 89.07811053685734, (53, 29750): 90.26336826033007, (53, 29759): 88.77943094053397, (53, 29772): 88.64640293309394, (53, 29781): 88.76022033484146, (53, 29784): 87.4939785513517, (53, 29790): 89.26191044536834, (53, 29811): 90.66349558408547, (53, 29817): 98.28471450792038, (53, 29818): 98.43466195699361, (53, 29929): 84.25098304136748, (53, 30039): 75.17658451476623, (53, 30066): 70.73059189570971, (53, 30116): 79.97769177892029, (53, 30238): 94.65537190965348, (53, 30248): 79.36900410166002, (53, 30260): 78.5055014217989, (53, 30545): 308.44984192200906, (53, 30733): 289.01019473778746, (53, 30756): 284.5113246933661, (53, 30921): 293.58278502945257, (53, 31079): 239.6070052777883, (53, 31149): 238.30445582049785, (53, 31154): 238.15472539770857, (53, 31160): 238.18855237790376, (53, 31163): 237.86562018385843, (53, 31189): 230.6961774710571, (53, 31215): 230.9282140790151, (53, 31259): 229.0729471236384, (53, 31262): 228.35038685338245, (53, 31430): 239.78516778488796, (53, 31568): 217.0399893717813, (53, 31751): 235.06208547012508, (55, 109): 269.6294261264595, (55, 872): 144.67571391249191, (55, 873): 144.37797782613234, (55, 877): 144.03335356394425, (55, 879): 143.94476118337857, (55, 884): 143.22878527668811, (55, 889): 143.2550822090658, (55, 891): 143.4516250037476, (55, 892): 143.8097492626195, (55, 894): 144.03394430237316, (55, 896): 145.07634638975756, (55, 903): 143.501642948537, (55, 909): 145.5063780870046, (55, 910): 145.80772109916282, (55, 912): 145.90710505346263, (55, 913): 145.86440458892235, (55, 916): 146.46126939509634, (55, 926): 146.26515845648234, (55, 927): 146.45888399601554, (55, 948): 143.63577131378813, (55, 961): 145.2878834492188, (55, 962): 145.54869334528817, (55, 963): 145.7470894979484, (55, 967): 143.56074670484387, (55, 974): 142.65742769314733, (55, 998): 143.0679726712017, (55, 1014): 143.44858984289533, (55, 1086): 157.66497808472434, (55, 1087): 159.20887305350337, (55, 1089): 158.64927667037517, (55, 1090): 158.41902577225318, (55, 1092): 158.05585882015492, (55, 1097): 158.03404275347515, (55, 1107): 158.83846464921763, (55, 1387): 228.71340936911844, (55, 1554): 234.30657528709258, (55, 1827): 125.28952920623718, (55, 1828): 125.50569671429123, (55, 1829): 125.33759485666857, (55, 1830): 124.29017256923234, (55, 1831): 124.47092491934688, (55, 1832): 124.58375966987316, (55, 1833): 124.76489104946617, (55, 1836): 124.98099230651064, (55, 1841): 124.65301528481018, (55, 1843): 124.6779528681397, (55, 1844): 124.48596436727452, (55, 1845): 124.35712990880846, (55, 1847): 124.99267562172186, (55, 1848): 124.89149744848594, (55, 1849): 124.24645470990424, (55, 1850): 124.36701793339249, (55, 1851): 124.33033640074807, (55, 1852): 123.9045534637597, (55, 1854): 124.18861914669972, (55, 1856): 124.45125737191508, (55, 1857): 124.66900016578089, (55, 1858): 124.5822509297229, (55, 1861): 124.98117182145901, (55, 1866): 124.09450910700782, (55, 1867): 125.00618030523928, (55, 1868): 125.37001139756326, (55, 1870): 123.94713543647693, (55, 1871): 125.3647773129324, (55, 1875): 124.47683553980374, (55, 1880): 124.77035220747099, (55, 1882): 124.14517983581526, (55, 1883): 124.84271502742143, (55, 1889): 125.43142065641675, (55, 1893): 126.0218088856465, (55, 1894): 126.17688741276055, (55, 1899): 125.75147120952826, (55, 1900): 125.86808399693342, (55, 1902): 125.9617025096795, (55, 1905): 125.64228853710742, (55, 1907): 125.278157088061, (55, 1910): 125.78048121924317, (55, 1917): 126.92764938413487, (55, 1920): 125.64512593729893, (55, 1935): 126.44602408793924, (55, 1937): 126.27139933611178, (55, 1946): 126.78169820050819, (55, 1949): 126.96545861422429, (55, 1950): 126.01421710830239, (55, 1951): 126.24065774963887, (55, 1952): 125.11868193570174, (55, 1953): 126.1062796534783, (55, 1954): 125.39425052034319, (55, 1958): 126.51997725530444, (55, 1960): 126.20388188513013, (55, 1968): 126.08204736862635, (55, 1969): 127.25628881652666, (55, 1974): 126.87396416857486, (55, 1975): 126.60020735600284, (55, 1979): 127.16074723556848, (55, 1980): 126.34460333716703, (55, 1981): 126.85294072714865, (55, 1985): 127.07575160243965, (55, 1994): 124.16772712505866, (55, 2011): 123.86741655639204, (55, 2019): 122.5903613443142, (55, 2020): 122.75081238929309, (55, 2029): 122.57096036593602, (55, 2030): 122.87524784767953, (55, 2032): 122.13165766648761, (55, 2033): 122.626633919486, (55, 2034): 122.22382386690026, (55, 2036): 120.52367627776655, (55, 2037): 121.02149855978696, (55, 2038): 122.90775698996558, (55, 2042): 122.349112240841, (55, 2050): 123.23807530768127, (55, 2051): 122.81274130187036, (55, 2053): 122.98765233485615, (55, 2054): 122.92140273812966, (55, 2066): 122.98064554598369, (55, 2067): 123.20234900725396, (55, 2071): 124.48675910000544, (55, 2072): 124.72363512213623, (55, 2073): 126.05560293043717, (55, 2074): 125.79331430662405, (55, 2080): 125.24657981140031, (55, 2082): 124.75583284366644, (55, 2083): 124.90640861151202, (55, 2089): 125.27675931767962, (55, 2090): 125.48988341767038, (55, 2092): 125.76568950488635, (55, 2098): 125.74674344548283, (55, 2099): 125.45461996026836, (55, 2101): 125.37827142286928, (55, 2102): 125.70791264957711, (55, 2103): 125.44869974655988, (55, 2104): 125.12977641172895, (55, 2106): 124.72162349094955, (55, 2112): 125.06989032627136, (55, 2113): 125.52392724987119, (55, 2114): 124.95238530929933, (55, 2117): 124.43797419391485, (55, 2123): 139.0831121009046, (55, 2124): 139.16174992576978, (55, 2134): 137.93838884008738, (55, 2138): 138.5670812447514, (55, 2141): 138.27296569674738, (55, 2148): 134.5001591892257, (55, 2150): 137.90366666197974, (55, 2151): 137.69762655172053, (55, 2152): 137.59860708047663, (55, 2153): 134.89588558368925, (55, 2154): 134.83420025308962, (55, 2155): 134.14471561380392, (55, 2156): 134.55894032840874, (55, 2157): 132.2425289695808, (55, 2160): 136.80348341980945, (55, 2161): 137.20119479391914, (55, 2162): 133.4354372340053, (55, 2163): 133.46258403899733, (55, 2164): 133.2197269588669, (55, 2168): 135.9437865134931, (55, 2172): 134.23274482868365, (55, 2174): 137.2003883372774, (55, 2178): 133.7700284971102, (55, 2179): 133.57632794578387, (55, 2183): 138.11188845377487, (55, 2185): 137.8764948841595, (55, 2186): 137.94194128696205, (55, 2190): 137.2440861840754, (55, 2192): 137.27816223489327, (55, 2193): 138.26819321508378, (55, 2194): 138.30190378364014, (55, 2195): 137.79186805446278, (55, 2197): 137.01857798901003, (55, 2205): 136.3398246729905, (55, 2207): 135.62500376651622, (55, 2208): 135.92139213349722, (55, 2212): 139.38886397846713, (55, 2214): 131.2229039002665, (55, 2225): 129.75511181958205, (55, 2231): 140.57470009784706, (55, 2278): 126.35452243711934, (55, 2284): 125.50427536434906, (55, 2285): 125.16813784364686, (55, 2291): 122.97310615066827, (55, 2292): 125.67137460776397, (55, 2307): 125.44966807817437, (55, 2313): 122.13829897524857, (55, 2317): 126.79048737628172, (55, 2319): 125.39321786561347, (55, 2321): 124.93070958328636, (55, 2323): 125.69563641811911, (55, 2326): 127.07274035779668, (55, 2327): 127.08471465623595, (55, 2329): 127.01477988119379, (55, 2330): 126.7557458417636, (55, 2332): 126.37410679740829, (55, 2344): 127.50980696400144, (55, 2346): 126.97735733590527, (55, 2361): 131.43744177891764, (55, 2368): 128.7876898607935, (55, 2374): 128.37200725463873, (55, 2375): 128.64008216611117, (55, 2377): 129.05712100171974, (55, 2378): 128.4076427043099, (55, 2379): 127.86618216969275, (55, 2380): 128.2473921305765, (55, 2383): 129.37440883792888, (55, 2385): 129.556698319115, (55, 2395): 130.03485871772907, (55, 2397): 127.62598777084106, (55, 2398): 129.13424075526828, (55, 2399): 129.35665703214283, (55, 2400): 129.37370212000525, (55, 2402): 127.8254351786228, (55, 2403): 127.77159151279916, (55, 2404): 127.97910051961745, (55, 2405): 127.91085228067699, (55, 2407): 128.28660238071583, (55, 2408): 127.99556584786748, (55, 2409): 128.01523303999699, (55, 2411): 126.87424673244196, (55, 2412): 127.22493003579727, (55, 2413): 127.05799770222546, (55, 2414): 127.00724393477913, (55, 2422): 126.57731550993248, (55, 2424): 127.40687149849568, (55, 2426): 127.57821757915892, (55, 2433): 127.3194855741259, (55, 2436): 126.75668012293137, (55, 2437): 127.22683711622406, (55, 2440): 127.28027157653884, (55, 2445): 121.38270095352459, (55, 2447): 121.98568469505481, (55, 2454): 121.91802599031143, (55, 2455): 122.34809018273316, (55, 2460): 122.00928026005657, (55, 2461): 121.95142720977124, (55, 2471): 119.22578746318503, (55, 2492): 102.67621500849172, (55, 2511): 105.74752592401633, (55, 2523): 104.10483442813359, (55, 2525): 103.23205778596406, (55, 2535): 112.08472396527779, (55, 2537): 111.85090305663849, (55, 2538): 112.44285203895646, (55, 2539): 110.32356185206397, (55, 2540): 112.13828588080382, (55, 2542): 111.56750583038148, (55, 2559): 116.84608624595735, (55, 2575): 114.15952037169416, (55, 2599): 119.32584488331398, (55, 2600): 117.91042467109513, (55, 2607): 120.35033677345383, (55, 2627): 98.09550640361452, (55, 2647): 96.56416047790798, (55, 2674): 98.90459531500562, (55, 2681): 97.80091911567314, (55, 2683): 98.26482992987671, (55, 2686): 98.85115620348775, (55, 2689): 98.07812268791038, (55, 2690): 97.8122068223201, (55, 2713): 89.99158810174676, (55, 2714): 88.92548244648977, (55, 2715): 89.01910946220879, (55, 2739): 89.25765822891285, (55, 2740): 91.74464695043602, (55, 2741): 92.00282808355772, (55, 2749): 87.98325097301547, (55, 2750): 88.39794032189744, (55, 2752): 88.6383847645321, (55, 2755): 88.4657188444205, (55, 2758): 88.11951964903963, (55, 2759): 88.29367452533296, (55, 2769): 88.63080516617234, (55, 2771): 91.08495902190909, (55, 2779): 88.28688219805764, (55, 2784): 86.25273725486723, (55, 2800): 83.61039738851025, (55, 2802): 90.08700204598938, (55, 2803): 90.41261743036874, (55, 2804): 90.50452118458342, (55, 2805): 89.08224028493977, (55, 2807): 89.43522473214462, (55, 2809): 88.61023835281935, (55, 2812): 89.07619398454435, (55, 2814): 86.22506993287884, (55, 2817): 83.06124136703798, (55, 2819): 90.32034515302158, (55, 2823): 86.03146900465876, (55, 2832): 88.66745280814035, (55, 2836): 88.39948684536482, (55, 2839): 89.79693350436804, (55, 2841): 84.68670708694188, (55, 2843): 85.234349864724, (55, 2846): 87.01089483944946, (55, 2849): 88.109590402302, (55, 2852): 88.27384745501992, (55, 2853): 88.01246952056987, (55, 2876): 86.38255418815817, (55, 2877): 86.37919490129524, (55, 2885): 83.09203095600125, (55, 2918): 92.64141341794415, (55, 2921): 92.306260756829, (55, 2925): 95.06091599474492, (55, 2926): 96.65877439994198, (55, 2930): 91.22207008934922, (55, 2931): 94.10752971989254, (55, 2938): 92.02017958105442, (55, 2940): 95.21763743660281, (55, 2947): 95.69728647261383, (55, 2949): 92.62768799449263, (55, 2950): 92.05241004581349, (55, 2952): 91.99482524683326, (55, 2958): 92.23926604921331, (55, 2959): 92.98614475446341, (55, 2960): 92.83863980002644, (55, 2961): 92.51474517810605, (55, 2963): 91.85170056619047, (55, 2968): 91.51252118657608, (55, 2976): 92.21312555514808, (55, 2981): 87.12270059451065, (55, 2982): 86.3763360600431, (55, 2984): 86.17411588009382, (55, 3003): 85.31007982959493, (55, 3046): 93.2261041798388, (55, 3050): 89.58211821438483, (55, 3051): 89.88461711264863, (55, 3053): 89.50869167038812, (55, 3069): 88.73963462284665, (55, 3071): 91.15424930492212, (55, 3080): 81.8871783837829, (55, 3199): 80.7762122661737, (55, 3200): 80.19657388540617, (55, 3205): 81.24318198310604, (55, 3209): 80.16277912298268, (55, 3215): 80.60076856632968, (55, 3217): 80.38162692498754, (55, 3249): 81.04024004687054, (55, 3263): 83.07372167094162, (55, 3289): 82.71793033494916, (55, 3301): 81.73793025197443, (55, 3302): 82.03411683365606, (55, 3307): 82.03837888849296, (55, 3310): 81.84021004983087, (55, 3391): 62.32583490939842, (55, 3509): 132.96523819086494, (55, 3510): 133.3354383297254, (55, 3511): 133.37048645652175, (55, 3512): 133.84579030126048, (55, 3514): 133.99298046943747, (55, 3519): 130.72508206762407, (55, 3536): 132.8157392403533, (55, 3545): 132.5344644331691, (55, 3548): 133.4680696451215, (55, 3572): 132.26133091225788, (55, 3581): 131.7682662543661, (55, 3583): 133.178126476083, (55, 3601): 129.59193859924676, (55, 3656): 129.150907948795, (55, 3669): 127.71380103242147, (55, 3670): 127.27061791106772, (55, 3695): 130.1768867358174, (55, 3696): 129.93640002862125, (55, 3782): 138.51772994458068, (55, 3792): 138.08313001273, (55, 3989): 313.99037554064955, (55, 4008): 316.01825358486735, (55, 4031): 314.93359037682717, (55, 4045): 315.1214184286997, (55, 4144): 316.12158594881157, (55, 4145): 315.04105937232765, (55, 4164): 315.5635209251688, (55, 4168): 315.37849536890366, (55, 4173): 315.4725693038333, (55, 4181): 314.22819558862227, (55, 4228): 312.04468768993337, (55, 4248): 312.8986183639767, (55, 4254): 305.8370607102309, (55, 4260): 305.4547331708426, (55, 4262): 306.44634643996153, (55, 4273): 306.01837552509977, (55, 4319): 301.4135117026053, (55, 4326): 301.0997049668592, (55, 4328): 301.07560601130416, (55, 4334): 301.80837202319236, (55, 4335): 301.7223288447164, (55, 4372): 318.32849753532764, (55, 4413): 327.2743660553073, (55, 4434): 317.8914524516061, (55, 4447): 318.813022425026, (55, 4452): 318.0479207040367, (55, 4463): 301.5786995411348, (55, 4465): 302.10411951131545, (55, 4619): 328.84943731804884, (55, 4645): 330.625545306023, (55, 4657): 330.3964182719372, (55, 4666): 329.7303825964592, (55, 4676): 331.02637739981145, (55, 4678): 331.2862838563083, (55, 4689): 330.47561969884606, (55, 4704): 336.92031965409194, (55, 4726): 353.3740114526268, (55, 4727): 353.0761739202764, (55, 4730): 352.49763598392104, (55, 4731): 352.66849592437757, (55, 4734): 352.9644779988776, (55, 4735): 352.68680110860095, (55, 4736): 352.83346272135617, (55, 4737): 352.3376881139705, (55, 4738): 352.4078156620889, (55, 4756): 352.708224903718, (55, 4760): 351.18834426621964, (55, 4761): 351.3471365767535, (55, 4762): 350.78609132639605, (55, 4765): 351.33830454737034, (55, 4773): 353.9566687978034, (55, 4774): 353.6896862725975, (55, 4790): 353.75896353556726, (55, 4795): 353.4990513249508, (55, 4799): 353.81752829538163, (55, 4801): 354.4377010706832, (55, 4804): 353.6011912127762, (55, 4805): 353.3873768367278, (55, 4806): 353.57412825060027, (55, 4815): 353.28716699140455, (55, 4816): 354.0333886230466, (55, 4817): 354.1777255548999, (55, 4826): 353.73508950460297, (55, 4830): 353.3113333836488, (55, 4839): 352.0577886548088, (55, 4840): 352.3246548834137, (55, 4841): 351.6966892421919, (55, 4846): 351.48963724582563, (55, 4848): 351.42322927655084, (55, 4850): 351.69439158605115, (55, 4871): 348.21772601683955, (55, 4883): 350.8486711482938, (55, 4900): 349.49113193007, (55, 4901): 349.12231987013024, (55, 4917): 328.83759478319234, (55, 4931): 326.65701902378885, (55, 4944): 329.08515765591005, (55, 4956): 327.05663239638136, (55, 4958): 326.9924377224502, (55, 4959): 326.57757032024904, (55, 4961): 327.49847506803684, (55, 4966): 326.5232438261138, (55, 5207): 324.1071091366951, (55, 5272): 281.0757612670393, (55, 5283): 281.91166394740054, (55, 5287): 283.3550318279926, (55, 5289): 283.7242323231121, (55, 5293): 281.1116989441631, (55, 5295): 283.4366738989261, (55, 5296): 283.49047323133306, (55, 5298): 283.5016304142653, (55, 5303): 284.24391958851805, (55, 5305): 280.7343562667469, (55, 5306): 280.18966016680685, (55, 5307): 280.31046422464277, (55, 5308): 281.1380353240627, (55, 5313): 281.0140071004571, (55, 5314): 281.5100723839343, (55, 5317): 281.1884113832308, (55, 5319): 283.463039597498, (55, 5324): 282.9430901500443, (55, 5326): 282.6035194905454, (55, 5348): 280.0571919958521, (55, 5351): 280.7628512246638, (55, 5399): 284.28636416521124, (55, 5413): 281.95522185485595, (55, 5422): 284.6681559386993, (55, 5445): 282.81143354612607, (55, 5448): 282.0263521887345, (55, 5456): 281.9128539328431, (55, 5467): 282.66021103780736, (55, 5624): 273.7617887599725, (55, 5671): 298.43122262502817, (55, 5672): 297.3373599297276, (55, 5797): 311.3407624368482, (55, 5871): 295.74135112088914, (55, 5976): 286.6207077545573, (55, 6118): 67.60994779126979, (55, 6248): 51.65416976039061, (55, 6345): 221.82846045112456, (55, 6352): 219.24483921084243, (55, 6354): 222.56031894097194, (55, 6359): 222.89293804303085, (55, 6376): 219.22077425612872, (55, 6378): 222.23350680558664, (55, 6381): 222.5582269392113, (55, 6383): 221.35169864732345, (55, 6396): 221.57198027854128, (55, 6399): 221.64689596379324, (55, 6408): 219.51745375595854, (55, 6409): 221.21023165143112, (55, 6419): 217.8149933345528, (55, 6422): 220.23224856827542, (55, 6423): 220.05083649171473, (55, 6424): 222.84398981266148, (55, 6439): 222.50547843575657, (55, 6464): 221.94391223036422, (55, 6465): 221.5191678275875, (55, 6469): 221.48999120494375, (55, 6470): 221.25159530599856, (55, 6472): 223.69954367892694, (55, 6480): 223.95732764008528, (55, 6486): 226.3626751412888, (55, 6497): 225.595488578634, (55, 6503): 223.12629304198342, (55, 6508): 222.75472669070479, (55, 6509): 223.50325940740748, (55, 6521): 224.64604288282803, (55, 6544): 224.99317154949532, (55, 6552): 221.55298617558947, (55, 6553): 221.20856017778988, (55, 6554): 220.851191804392, (55, 6578): 222.05249725736525, (55, 6582): 222.3378758853383, (55, 6601): 222.32774993770568, (55, 6609): 224.66541590779167, (55, 6610): 224.88295928027463, (55, 6611): 224.6621211797087, (55, 6614): 224.2974404559018, (55, 6615): 224.46646406692494, (55, 6616): 225.22973892294524, (55, 6617): 224.927308239395, (55, 6618): 225.857103913421, (55, 6619): 224.08895376125488, (55, 6620): 225.42148036175357, (55, 6621): 225.14660831699268, (55, 6622): 225.09206521700472, (55, 6623): 224.46128026547453, (55, 6624): 224.37331319482013, (55, 6625): 224.21604753448347, (55, 6626): 223.99257369279454, (55, 6627): 224.06311915370244, (55, 6628): 225.5451628215893, (55, 6629): 224.6857770181321, (55, 6630): 223.65560049429206, (55, 6632): 224.55151060281247, (55, 6634): 223.43285597221097, (55, 6635): 224.93446337035874, (55, 6636): 225.31088716009177, (55, 6637): 224.27664124195732, (55, 6638): 223.86636696675228, (55, 6639): 224.20041458035794, (55, 6640): 223.8273619226055, (55, 6641): 225.28367192633743, (55, 6642): 223.99492294235466, (55, 6643): 223.8288665201773, (55, 6645): 224.21514620811206, (55, 6646): 225.59943142865754, (55, 6647): 224.02196301330642, (55, 6653): 224.3965893132083, (55, 6655): 224.14558753200313, (55, 6658): 223.4806243628887, (55, 6662): 224.10767181347282, (55, 6819): 208.97067649932055, (55, 6996): 218.09641305227032, (55, 7059): 222.04522715755974, (55, 7187): 223.1342411110721, (55, 7304): 210.15957003443643, (55, 7528): 221.0271122413494, (55, 7720): 242.01626866396757, (55, 7793): 242.69897018973953, (55, 7807): 242.640892677638, (55, 7808): 242.85528286753743, (55, 7831): 228.21854865982243, (55, 7850): 231.20395301963177, (55, 7852): 230.04927393405026, (55, 8012): 239.26643694845598, (55, 8125): 250.82481653305143, (55, 8208): 249.62783137566456, (55, 8392): 234.29446059120187, (55, 8651): 190.17825679908768, (55, 9088): 203.7681788520583, (55, 9443): 194.2638211547946, (55, 9444): 194.99556399064448, (55, 9828): 185.43922712939207, (55, 9868): 178.53306810940765, (55, 10180): 251.76401410137248, (55, 10256): 262.56062213550064, (55, 10276): 256.61554355393287, (55, 10378): 254.82076376308768, (55, 10676): 253.22446238720133, (55, 10714): 247.8845930629966, (55, 10730): 245.3656589250998, (55, 10862): 271.19451030413165, (55, 10881): 272.8720830173117, (55, 10883): 272.73380093267707, (55, 10885): 270.8216702181635, (55, 10891): 272.52306240496654, (55, 10909): 272.26223574892646, (55, 10911): 272.3807857683385, (55, 10913): 272.0312766645031, (55, 10915): 271.9535695018089, (55, 10919): 272.1364681675738, (55, 11037): 262.3515160027622, (55, 11039): 257.5373576089619, (55, 11516): 326.4129621960541, (55, 11856): 302.0550516867982, (55, 11857): 302.16635656792084, (55, 11861): 302.1350362984341, (55, 11881): 301.0992353223081, (55, 11902): 299.3624067788181, (55, 11911): 298.5786183673196, (55, 11914): 299.0248615166242, (55, 11922): 300.4782143477337, (55, 11924): 300.76693025193504, (55, 11926): 300.2388343453823, (55, 11950): 300.70860669851174, (55, 11963): 302.41789636427075, (55, 11983): 300.4369827819166, (55, 11985): 303.3190604024661, (55, 12009): 302.26105417836294, (55, 12010): 301.23234598761024, (55, 12018): 301.33229668970483, (55, 12020): 301.76532556000524, (55, 12021): 301.8845035526312, (55, 12024): 303.03618815088606, (55, 12025): 302.7962807818939, (55, 12027): 302.48660185416867, (55, 12031): 301.03512500923375, (55, 12032): 301.55131967451615, (55, 12035): 302.0151880315584, (55, 12041): 303.89024141976256, (55, 12045): 287.2367555166097, (55, 12145): 293.7724330891004, (55, 12275): 312.9856071838279, (55, 12294): 309.00144231707645, (55, 12358): 317.61866919769784, (55, 12463): 320.37920409733346, (55, 12465): 320.2151892639545, (55, 12482): 322.6426514437756, (55, 12503): 322.215608335926, (55, 12506): 322.6793543988429, (55, 12549): 322.6196209303994, (55, 12559): 322.07718452399405, (55, 12569): 322.12274452287886, (55, 12572): 322.49090346857656, (55, 12574): 321.82575649702886, (55, 12576): 323.13734058458033, (55, 12591): 323.596211975258, (55, 12608): 326.8383631859211, (55, 12696): 322.6388104220363, (55, 12710): 326.0225909017506, (55, 12728): 323.95134387770526, (55, 12766): 251.8532811450583, (55, 12771): 250.7747156218439, (55, 12790): 250.30050798320033, (55, 12795): 248.9667638518573, (55, 12797): 246.3807793764662, (55, 12798): 246.97208780926778, (55, 12811): 249.85115996787087, (55, 12830): 248.51292188873566, (55, 12848): 249.7698376095123, (55, 12850): 250.46709264672262, (55, 12852): 248.60000753574724, (55, 12854): 248.1506873626839, (55, 12859): 250.41506484126768, (55, 12861): 247.63647395083373, (55, 12865): 250.07397699578542, (55, 12866): 250.0627130057212, (55, 12867): 250.7675491131832, (55, 12874): 250.39464329344867, (55, 12875): 250.83036571622674, (55, 12881): 249.1784287931731, (55, 12883): 249.76157705280227, (55, 12885): 251.07662685143012, (55, 12888): 249.64837330472696, (55, 12889): 249.66648393360873, (55, 12892): 250.4067873663931, (55, 12893): 249.51746058917263, (55, 12896): 249.9402647117057, (55, 12906): 249.75472841013365, (55, 13018): 241.76536804681461, (55, 13071): 240.96526263464798, (55, 13131): 240.652126473923, (55, 13146): 244.42686167973295, (55, 13159): 235.7676300157731, (55, 13193): 240.31255153326703, (55, 13198): 236.4160280854794, (55, 13292): 242.9861696047421, (55, 13296): 246.30099343798872, (55, 13406): 230.63719990178157, (55, 13407): 230.2678264523559, (55, 13417): 228.34534743947646, (55, 13418): 228.68826535876934, (55, 13438): 232.25495865510172, (55, 13442): 233.23163153670046, (55, 13443): 232.70664833631466, (55, 13764): 181.15360731868037, (55, 13766): 181.79790897378723, (55, 13771): 180.6526670076378, (55, 13783): 181.49104080183125, (55, 13784): 182.72424162067395, (55, 13792): 178.63752038162798, (55, 13824): 180.94526391049743, (55, 14017): 187.82993813891298, (55, 14870): 268.66656334099, (55, 14997): 220.98527701552257, (55, 15000): 221.4219010915578, (55, 15003): 222.2048948442922, (55, 15006): 221.45113950854318, (55, 15007): 221.90064155466018, (55, 15056): 222.9733869389516, (55, 15063): 222.8298807327434, (55, 15069): 223.12482133081218, (55, 15076): 222.23079290141916, (55, 15086): 220.4618739422448, (55, 15087): 220.54390670023346, (55, 15111): 218.93717295277668, (55, 15116): 219.898009723837, (55, 15722): 208.79338228771266, (55, 15998): 211.9947455892819, (55, 16073): 86.0035328493845, (55, 16939): 114.21217324340715, (55, 16940): 114.5142399856322, (55, 16951): 112.78483703048667, (55, 16963): 113.09794704662069, (55, 16965): 113.34376766734613, (55, 16969): 112.5589080080218, (55, 16970): 113.45569886817194, (55, 16971): 113.28806734766324, (55, 16973): 112.77902363595491, (55, 16974): 112.96439332460575, (55, 16976): 113.78542722615141, (55, 16978): 113.83616446431216, (55, 16980): 114.27556525019463, (55, 16982): 112.44045632145394, (55, 17045): 74.56781159107288, (55, 17048): 74.58128421589397, (55, 17304): 311.0598682449674, (55, 17305): 310.0767800988169, (55, 17330): 310.6419518385052, (55, 17334): 310.37659819249035, (55, 17343): 311.11534320484276, (55, 17345): 309.7408084065387, (55, 17347): 310.1915296220188, (55, 17351): 309.30895546217573, (55, 17372): 310.0593675482277, (55, 17373): 311.1617964550618, (55, 17377): 311.18950278082855, (55, 17382): 310.34321860600187, (55, 17383): 310.7039048497428, (55, 17389): 310.1552711074122, (55, 17400): 311.116473876776, (55, 17401): 311.19584685168195, (55, 17402): 311.1080320782127, (55, 17403): 311.1432652180377, (55, 17440): 309.134287078112, (55, 17455): 310.5662931492103, (55, 17491): 310.1977586353199, (55, 17507): 311.2648598774663, (55, 17509): 311.914514625005, (55, 17590): 308.3017709322028, (55, 17615): 309.4315952553064, (55, 17642): 309.627280881809, (55, 17643): 309.35208312220453, (55, 17668): 309.55684349408926, (55, 17721): 309.6871770672366, (55, 17754): 314.7879035430914, (55, 17769): 312.118831070023, (55, 17776): 309.02891458002756, (55, 17804): 313.04046821981035, (55, 17809): 313.54648352106193, (55, 17824): 313.5994808694159, (55, 17837): 310.34001380138596, (55, 17838): 310.05198576183693, (55, 17862): 309.5132975792544, (55, 17866): 310.749314644836, (55, 17872): 309.3595364861239, (55, 17873): 308.3388926481094, (55, 17881): 309.8541894645876, (55, 17947): 153.5811469604187, (55, 17951): 153.36986490902285, (55, 17953): 153.7331907417766, (55, 17954): 154.01063543725678, (55, 17959): 152.8417841316583, (55, 17963): 152.0692964328195, (55, 18000): 152.39198677080782, (55, 18001): 152.92840900220412, (55, 18111): 172.94257696362948, (55, 18148): 174.23488307963478, (55, 18166): 175.14491443936217, (55, 18189): 172.29348304610738, (55, 18239): 311.6473711682972, (55, 18240): 311.5699719418639, (55, 18245): 311.6574583652094, (55, 18247): 311.47130185168476, (55, 18251): 311.56863620289033, (55, 18256): 311.59090078558864, (55, 18258): 311.4234199920679, (55, 18259): 311.40765487636503, (55, 18260): 311.4028000467622, (55, 18262): 311.4462205427923, (55, 18263): 311.5833040084011, (55, 18264): 311.5830512366443, (55, 18266): 311.4199467487885, (55, 18267): 311.42976135351245, (55, 18268): 311.40785991034403, (55, 18269): 311.419779078678, (55, 18275): 311.4138344093533, (55, 18285): 311.6113390327397, (55, 18308): 311.47908149197156, (55, 18313): 311.2327824103288, (55, 18314): 311.1227591546986, (55, 18315): 311.61704165747284, (55, 18316): 311.517818855627, (55, 18317): 311.51735942902553, (55, 18320): 311.6557768876395, (55, 18321): 311.6122536430262, (55, 18322): 311.63102963024744, (55, 18324): 311.78310955189596, (55, 18325): 311.97475504683933, (55, 18326): 311.9077621907221, (55, 18327): 311.43676454401907, (55, 18329): 312.1679220548775, (55, 18330): 311.7738334508877, (55, 18331): 311.69274392696576, (55, 18332): 311.55973073600944, (55, 18333): 311.8391200874263, (55, 18336): 311.87492500279444, (55, 18337): 312.0012171682927, (55, 18403): 311.36548628185454, (55, 18432): 305.9789591939952, (55, 18451): 309.61090359502083, (55, 18466): 313.4242445468125, (55, 18481): 311.92046096367716, (55, 18483): 311.85290173983907, (55, 18484): 311.7991575813, (55, 18485): 311.7056390048797, (55, 18486): 312.228873635341, (55, 18487): 312.06499371304346, (55, 18489): 311.9709877494933, (55, 18490): 312.3989086140903, (55, 18491): 312.5146674111495, (55, 18492): 311.761364697616, (55, 18493): 312.2681288520074, (55, 18494): 311.86941778330754, (55, 18495): 312.3227632261417, (55, 18496): 312.1461476575258, (55, 18497): 312.08953219133315, (55, 18498): 311.8717802025846, (55, 18499): 312.0266145426734, (55, 18501): 312.03357780132626, (55, 18502): 311.94222157140143, (55, 18503): 311.7901198088535, (55, 18504): 312.1109194377853, (55, 18506): 312.24195475055996, (55, 18507): 312.19307387814695, (55, 18508): 312.0704121685512, (55, 18509): 312.13629895668464, (55, 18510): 311.88675765071105, (55, 18511): 312.43552778971775, (55, 18512): 312.1899061511204, (55, 18515): 312.21605500654704, (55, 18516): 312.4453396610057, (55, 18517): 312.4262292483612, (55, 18518): 312.4687446580812, (55, 18519): 312.0936797432321, (55, 18520): 311.9604303662462, (55, 18522): 312.3919633646591, (55, 18523): 312.4888237575976, (55, 18532): 312.7404681617638, (55, 18535): 312.29317474042676, (55, 18537): 312.044234720591, (55, 18539): 312.13461250790454, (55, 18540): 312.20410924882583, (55, 18541): 312.36014941265046, (55, 18542): 312.4522444056913, (55, 18543): 312.0248025660927, (55, 18546): 312.35234064243474, (55, 18555): 312.7495532663956, (55, 18556): 312.87177041390026, (55, 18565): 312.81022697245334, (55, 18567): 313.0700815664438, (55, 18568): 312.7919848287826, (55, 18577): 314.3150179935834, (55, 18583): 313.85774835308035, (55, 18605): 313.93577161274845, (55, 18608): 313.49410324591105, (55, 18616): 315.3735086847213, (55, 18618): 316.72677546502894, (55, 18625): 315.7721115653548, (55, 18645): 314.47473141667245, (55, 18646): 314.93206425645667, (55, 18653): 314.4270277674011, (55, 18654): 315.4298183997633, (55, 18655): 314.8805100401215, (55, 18666): 317.94625007039656, (55, 18837): 305.7706364569724, (55, 18974): 307.9032851800871, (55, 18999): 308.01603819920183, (55, 19000): 308.3597591483489, (55, 19174): 287.49785040397467, (55, 19342): 292.96891367575796, (55, 19455): 293.365134228123, (55, 19555): 274.58746663007554, (55, 19564): 273.7981631394717, (55, 19573): 273.469222026998, (55, 19586): 273.4376808517623, (55, 19605): 273.98535888085814, (55, 19611): 274.2752300835638, (55, 19614): 274.6258890920945, (55, 19641): 281.6739321031566, (55, 19702): 280.9971672842853, (55, 19713): 280.5931232910271, (55, 19731): 274.49548092450965, (55, 19819): 289.66999266488114, (55, 19893): 294.8602386272563, (55, 19899): 299.78727180839905, (55, 19929): 295.8873087553343, (55, 19951): 304.74770666924167, (55, 19962): 297.11843239837094, (55, 19970): 298.0330385946116, (55, 19971): 298.3126729221023, (55, 19972): 297.7415908323145, (55, 19975): 297.2236330272629, (55, 19978): 305.57554713322605, (55, 19987): 305.5728517945395, (55, 19989): 303.1445457304089, (55, 20039): 305.944417439745, (55, 20043): 306.7459838085441, (55, 20047): 305.7811920716724, (55, 20052): 303.2682376801121, (55, 20054): 303.5811216763652, (55, 20085): 314.3302717216692, (55, 20104): 315.04277129828034, (55, 20132): 310.8928839975526, (55, 20203): 296.5338245873007, (55, 20280): 296.2204518742751, (55, 20285): 296.2505352572648, (55, 20290): 296.50903485070796, (55, 20297): 295.64726275537834, (55, 20309): 307.7891691997691, (55, 20453): 318.74498349455905, (55, 20485): 290.2920736544772, (55, 20520): 288.07639865447686, (55, 20526): 288.00932010026804, (55, 20698): 154.74008261648166, (55, 20868): 130.96607265406408, (55, 21042): 259.3812164259773, (55, 21057): 263.2684265413259, (55, 21066): 261.8052161768955, (55, 21075): 260.4318526211151, (55, 21093): 260.2944023719298, (55, 21098): 263.9639757247079, (55, 21127): 260.03126436119567, (55, 21130): 261.06996049800057, (55, 21144): 260.374047746201, (55, 21146): 259.77369172022117, (55, 21147): 260.13346556889957, (55, 21148): 261.0175411015009, (55, 21153): 257.11311027178573, (55, 21293): 266.66746016006505, (55, 21426): 260.06241920642333, (55, 21442): 263.25365872976704, (55, 21451): 263.58859514200367, (55, 21466): 261.9413259037228, (55, 21469): 262.68778242318814, (55, 21471): 261.55077189392483, (55, 21473): 262.2354915401658, (55, 21475): 261.6980104711326, (55, 21482): 262.9338444378293, (55, 21484): 262.89727726461183, (55, 21488): 262.39800381504523, (55, 21494): 262.0073732186939, (55, 21498): 262.48331996886174, (55, 21500): 261.9780600621144, (55, 21514): 264.50128490052913, (55, 21537): 262.5329936807153, (55, 21662): 265.9274173365392, (55, 21691): 263.27777397150976, (55, 21757): 256.2012175301931, (55, 21777): 253.78628907028303, (55, 21778): 253.13085723533624, (55, 21779): 253.78964868999915, (55, 21790): 254.2083424932234, (55, 21802): 254.745815472948, (55, 21824): 255.717427814241, (55, 21874): 254.31884403191776, (55, 21879): 254.46982736481945, (55, 21983): 254.28426086449863, (55, 22002): 263.3536626451824, (55, 22132): 252.13650108478794, (55, 22261): 196.17133004279742, (55, 22298): 198.26013783020574, (55, 22339): 197.53533602927322, (55, 22508): 203.73308356967607, (55, 22841): 19.053303980606632, (55, 22842): 19.439329398831187, (55, 22874): 20.404276668162762, (55, 22941): 19.109069762202402, (55, 22956): 19.659352413821146, (55, 22960): 18.8086047569165, (55, 22968): 24.35688768522594, (55, 22970): 23.679238965175454, (55, 22974): 27.14542658577237, (55, 22980): 27.58143214041197, (55, 23025): 32.29717021429352, (55, 23028): 33.193847061720426, (55, 23081): 39.86085749460617, (55, 23104): 47.39286827338242, (55, 23147): 32.15401488453836, (55, 23298): 277.7056287817143, (55, 23376): 275.9095575788319, (55, 23381): 276.2004950991514, (55, 23529): 279.96930478700875, (55, 23556): 278.75420357442005, (55, 23718): 275.466993542568, (55, 24001): 288.12559677065065, (55, 24094): 293.8103899883408, (55, 24129): 295.6255983042352, (55, 24174): 292.78452050048367, (55, 24235): 297.434440331797, (55, 24259): 298.56376724470556, (55, 24260): 298.52641846774185, (55, 24261): 298.04707895322156, (55, 24305): 300.3902339987417, (55, 24306): 300.86790913354514, (55, 24307): 300.26314725081994, (55, 24308): 291.0745818759946, (55, 24498): 303.1498203419356, (55, 24499): 303.2346507976928, (55, 24500): 302.84732823527037, (55, 24668): 298.16176589116617, (55, 24711): 306.4894383858058, (55, 24756): 308.5977180258327, (55, 24788): 308.7623542794401, (55, 24809): 307.57831593064475, (55, 24813): 307.872195768793, (55, 24821): 307.7409114761921, (55, 24825): 307.98831226394935, (55, 24832): 307.37826214506913, (55, 24833): 307.64514166808334, (55, 24835): 307.9566036614278, (55, 24837): 308.274492699193, (55, 24840): 307.3919809537644, (55, 24841): 307.6903683983862, (55, 24844): 307.4787132634227, (55, 24845): 307.4304759911844, (55, 24846): 307.8174776238985, (55, 24849): 307.9987667839194, (55, 24850): 308.04475416151575, (55, 24863): 303.7991931243841, (55, 24866): 304.24718974994016, (55, 24885): 305.05971373246854, (55, 24886): 305.262820432856, (55, 24889): 305.72065030267174, (55, 24903): 305.8665829919283, (55, 24909): 303.74444216045254, (55, 24999): 322.37279941695334, (55, 25019): 321.18913890465114, (55, 25028): 322.2361724355853, (55, 25137): 300.6082672749156, (55, 25145): 301.3370925565998, (55, 25208): 312.2725070307174, (55, 25233): 311.3501648339209, (55, 25371): 298.95262961962544, (55, 25377): 296.32507533286457, (55, 25828): 257.0942047278978, (55, 25851): 249.86255190215067, (55, 25874): 255.85312023431885, (55, 25898): 259.7176362859466, (55, 25946): 256.41278134067113, (55, 26047): 271.23186438522697, (55, 26066): 278.97978067784703, (55, 26197): 272.97462955106465, (55, 26212): 243.48117374478005, (55, 26253): 242.17649443865926, (55, 26254): 242.52320870419678, (55, 26257): 243.45837221113607, (55, 26258): 242.5769339149771, (55, 26260): 242.99411226481814, (55, 26266): 241.39878125618407, (55, 26267): 242.06435114129485, (55, 26271): 242.21688991459186, (55, 26304): 246.43642031450779, (55, 26305): 246.0487298921825, (55, 26363): 256.87886520586795, (55, 26441): 216.23813492722326, (55, 26442): 215.97941645717626, (55, 26450): 216.45161252819474, (55, 26459): 217.90122573242235, (55, 26462): 218.4633550731664, (55, 26467): 217.3785277144428, (55, 26471): 216.9553808474255, (55, 26472): 216.7763518946229, (55, 26473): 216.58467028499845, (55, 26476): 214.66222278998367, (55, 26485): 217.0052515651903, (55, 26493): 216.26355183489443, (55, 26524): 218.93084922024502, (55, 26525): 218.58578973609212, (55, 26556): 217.1719688769853, (55, 26560): 218.39878394525354, (55, 26561): 218.90805685205683, (55, 26564): 216.94843777892498, (55, 26569): 218.57360026766403, (55, 26570): 218.2157402328834, (55, 26573): 217.52206797792027, (55, 26581): 216.9682220997131, (55, 26583): 217.40049864082326, (55, 26593): 216.25348523048478, (55, 26837): 216.7270277409358, (55, 26844): 216.75116001809002, (55, 26863): 215.31709362845572, (55, 26893): 214.79397169580722, (55, 26902): 214.77602773182593, (55, 26905): 216.04483607925079, (55, 26912): 215.63633505317122, (55, 26921): 215.14984978239866, (55, 26922): 213.25157126808543, (55, 27212): 244.85002093366677, (55, 27218): 246.04195046629977, (55, 27239): 244.6231672601277, (55, 27257): 244.1780257472453, (55, 27274): 244.38743269295833, (55, 27279): 243.90921543433913, (55, 27282): 243.91997657294692, (55, 27283): 244.83156566177993, (55, 27285): 244.1010960207373, (55, 27286): 243.28408174765767, (55, 27290): 243.8541278986391, (55, 27295): 244.56413334710976, (55, 27300): 244.5728924174965, (55, 27344): 242.47919650899064, (55, 27366): 241.9965638193379, (55, 27383): 243.10767583636817, (55, 27398): 244.25753410889905, (55, 27406): 244.6063860108179, (55, 27407): 244.9847123544971, (55, 27426): 248.17907521460438, (55, 27432): 247.21355763618726, (55, 27460): 248.24091198858298, (55, 27523): 234.59311909933263, (55, 27545): 243.11712419954088, (55, 27602): 240.62213010073694, (55, 27606): 241.26200410517868, (55, 27646): 231.63630905200256, (55, 27667): 231.1860564127768, (55, 27672): 231.53896239876838, (55, 27674): 231.3787007261772, (55, 27688): 232.79554964917196, (55, 27692): 231.0365665790498, (55, 27693): 231.0213294353218, (55, 27705): 230.59768752441678, (55, 27712): 230.24362909193312, (55, 27786): 255.91072749518935, (55, 27790): 260.8660071155411, (55, 27791): 261.5884201119874, (55, 27795): 255.3766077543205, (55, 27801): 258.6065295097276, (55, 27813): 255.36607202975844, (55, 27816): 256.3411854623652, (55, 27823): 258.7744176891216, (55, 27830): 257.4581415754474, (55, 27884): 228.25692851174372, (55, 27885): 231.18332188501574, (55, 27896): 229.61495835430807, (55, 27919): 229.90706345051277, (55, 27922): 229.67269815804724, (55, 27930): 229.20653208201892, (55, 27934): 228.95757933678712, (55, 27935): 228.62800584471927, (55, 27948): 220.67618218362423, (55, 27951): 227.23251300861585, (55, 28061): 176.07967231155993, (55, 28290): 179.50342460155414, (55, 28292): 177.65054964393445, (55, 28293): 178.98984279538644, (55, 28295): 177.74478391583796, (55, 28296): 178.84906090434797, (55, 28297): 180.35158007311125, (55, 28302): 179.2321244925409, (55, 28310): 90.09870454452849, (55, 28313): 87.8648527557892, (55, 28372): 91.37261131808846, (55, 28398): 91.06045020458302, (55, 28399): 90.9859984085415, (55, 28400): 90.63103803052283, (55, 28401): 92.01963758631986, (55, 28445): 87.07538507565471, (55, 28475): 95.29843938420498, (55, 28885): 300.43312679547046, (55, 28886): 300.19228693061757, (55, 28915): 300.97091661530766, (55, 28916): 300.51783807595604, (55, 28917): 300.42537333502844, (55, 28921): 300.996717854965, (55, 28931): 301.024792588588, (55, 28945): 300.83105036002627, (55, 28982): 300.74271236107876, (55, 29219): 305.30660878901097, (55, 29228): 303.5565187250955, (55, 29246): 316.1408965645165, (55, 29248): 316.44203501934084, (55, 29282): 313.92417821305895, (55, 29290): 316.84792460483817, (55, 29291): 316.4920860721371, (55, 29292): 316.89154494682697, (55, 29293): 315.9301982956545, (55, 29294): 316.89048897420827, (55, 29298): 316.12479606130006, (55, 29299): 316.16617311919583, (55, 29304): 314.9951624390585, (55, 29317): 312.527522631071, (55, 29323): 312.3219196140215, (55, 29330): 313.5321843388571, (55, 29331): 314.02968361580884, (55, 29344): 306.44800231913865, (55, 29445): 288.5091907378113, (55, 29724): 12.5, (55, 29738): 12.5, (55, 29745): 12.5, (55, 29748): 12.5, (55, 29750): 12.5, (55, 29759): 12.5, (55, 29772): 12.5, (55, 29781): 12.5, (55, 29784): 12.5, (55, 29790): 12.5, (55, 29811): 12.5, (55, 29817): 12.5, (55, 29818): 12.5, (55, 29929): 12.5, (55, 30039): 13.630153242659377, (55, 30066): 17.419182026342597, (55, 30116): 14.247213502964227, (55, 30238): 29.529638258358457, (55, 30248): 23.103820204704075, (55, 30260): 23.34498316322536, (55, 30545): 293.07830851418817, (55, 30733): 274.01382968518874, (55, 30756): 272.3774062682468, (55, 30921): 279.80445970823314, (55, 31079): 217.5877461038221, (55, 31149): 218.84784582240454, (55, 31154): 218.33868447965918, (55, 31160): 218.808124695428, (55, 31163): 218.11384681538686, (55, 31189): 213.45037269905112, (55, 31215): 213.20186941923274, (55, 31259): 209.9846595326908, (55, 31262): 209.62557475242872, (55, 31430): 216.55420192059552, (55, 31568): 196.33465311382082, (55, 31751): 213.23845979049574}
    costs_LTL = {(1, 109): 331.6223884844872, (1, 872): 762.2982084298083, (1, 873): 764.6821982622465, (1, 877): 763.6917391594841, (1, 879): 764.0360068729015, (1, 884): 761.4248712043479, (1, 889): 762.9648458577655, (1, 891): 760.6621035850987, (1, 892): 765.9039610521671, (1, 894): 765.6424041900328, (1, 896): 763.5045857771609, (1, 903): 763.6711002231607, (1, 909): 759.9270222866483, (1, 910): 760.9704397054418, (1, 912): 759.3723824060161, (1, 913): 757.579018193485, (1, 916): 756.9492207706007, (1, 926): 761.8688294269899, (1, 927): 761.0876797150113, (1, 948): 759.813643564523, (1, 961): 761.5763180623653, (1, 962): 761.9089020999219, (1, 963): 762.262678709627, (1, 967): 764.7182258382539, (1, 974): 763.2129980274686, (1, 998): 765.5819845231119, (1, 1014): 818.8626447976104, (1, 1086): 758.8500043219609, (1, 1087): 758.817018469558, (1, 1089): 756.4641312159587, (1, 1090): 757.4530588379808, (1, 1092): 760.909084437354, (1, 1097): 758.2198401983286, (1, 1107): 762.79946734097, (1, 1387): 398.93295333907116, (1, 1554): 360.7328033566534, (1, 1827): 868.7176998522449, (1, 1828): 869.0274238189575, (1, 1829): 869.3538763097821, (1, 1830): 868.7081512414791, (1, 1831): 868.9696419951257, (1, 1832): 868.7394477258498, (1, 1833): 868.8143492135051, (1, 1836): 868.5918107458353, (1, 1841): 870.0492795698382, (1, 1843): 869.4102691916638, (1, 1844): 869.6489483770264, (1, 1845): 868.8478436101377, (1, 1847): 866.52029480196, (1, 1848): 867.3517862964526, (1, 1849): 871.2026652387268, (1, 1850): 871.6534422433106, (1, 1851): 867.8654824833476, (1, 1852): 867.8201378353506, (1, 1854): 868.3026037305933, (1, 1856): 866.2615084505426, (1, 1857): 867.2370198839657, (1, 1858): 870.8977085754437, (1, 1861): 869.209904545235, (1, 1866): 866.1163382783508, (1, 1867): 870.1830407915473, (1, 1868): 869.7566979430707, (1, 1870): 869.4411262475155, (1, 1871): 870.1564009200664, (1, 1875): 868.3321824187316, (1, 1880): 866.8791111019063, (1, 1882): 866.9741618158752, (1, 1883): 871.8070354588103, (1, 1889): 867.4937196399895, (1, 1893): 869.5723461059041, (1, 1894): 869.0051166109979, (1, 1899): 867.0394107930177, (1, 1900): 867.5154057483966, (1, 1902): 870.6085026706111, (1, 1905): 871.3097110194528, (1, 1907): 868.0322083301329, (1, 1910): 868.4466089949639, (1, 1917): 873.2745610597261, (1, 1920): 868.1829833898647, (1, 1935): 871.6174868817809, (1, 1937): 872.2395198291618, (1, 1946): 865.9486120912926, (1, 1949): 866.7397925425781, (1, 1950): 863.8845277503947, (1, 1951): 865.2051190250536, (1, 1952): 865.872412218215, (1, 1953): 866.5288991437202, (1, 1954): 865.756678914873, (1, 1958): 866.4178908378763, (1, 1960): 867.606483545726, (1, 1968): 868.0761012479434, (1, 1969): 871.9705782490206, (1, 1974): 870.9341852042318, (1, 1975): 870.8571500046254, (1, 1979): 869.1961571089063, (1, 1980): 868.8561756903032, (1, 1981): 869.5055797374271, (1, 1985): 869.9925678890297, (1, 1994): 862.4106882267437, (1, 2011): 866.8733206087146, (1, 2019): 872.8318902945547, (1, 2020): 872.0425492365051, (1, 2029): 868.8471094885448, (1, 2030): 871.498603995732, (1, 2032): 868.2219951981134, (1, 2033): 870.0197672878519, (1, 2034): 869.8901322736572, (1, 2036): 866.3107856121712, (1, 2037): 867.2433866131004, (1, 2038): 867.9875227302301, (1, 2042): 877.4092568211727, (1, 2050): 869.7410736286303, (1, 2051): 869.4971903395957, (1, 2053): 869.7947277077276, (1, 2054): 870.6247630071592, (1, 2066): 868.9166335022425, (1, 2067): 868.9772565202827, (1, 2071): 860.8890066965454, (1, 2072): 862.5365738856818, (1, 2073): 858.4943750709186, (1, 2074): 858.2156357306873, (1, 2080): 855.3950160056195, (1, 2082): 863.4015170368826, (1, 2083): 864.2598201492976, (1, 2089): 862.6048928065014, (1, 2090): 863.4230406035556, (1, 2092): 862.4427546828606, (1, 2098): 856.5437765923594, (1, 2099): 857.4012826122673, (1, 2101): 856.2888124337836, (1, 2102): 860.7085625125716, (1, 2103): 859.282552994386, (1, 2104): 858.460411315637, (1, 2106): 864.7704703674134, (1, 2112): 856.7932340555328, (1, 2113): 861.2827773050863, (1, 2114): 862.193268172511, (1, 2117): 865.3534897466772, (1, 2123): 862.2693280937665, (1, 2124): 863.1809311309457, (1, 2134): 860.3797548080064, (1, 2138): 863.1436681732963, (1, 2141): 860.7585100299889, (1, 2148): 861.2869196708951, (1, 2150): 858.5020826741519, (1, 2151): 859.4032763031983, (1, 2152): 857.9440874458104, (1, 2153): 861.6726416526743, (1, 2154): 857.9475338859504, (1, 2155): 857.3745437444314, (1, 2156): 856.7710013329755, (1, 2157): 857.2197166217915, (1, 2160): 864.034799870234, (1, 2161): 857.7079562584361, (1, 2162): 861.5196041911871, (1, 2163): 860.2671419749948, (1, 2164): 860.1311157436767, (1, 2168): 858.460875986112, (1, 2172): 858.939456135838, (1, 2174): 859.1930036539926, (1, 2178): 859.5768047564013, (1, 2179): 858.956153645546, (1, 2183): 862.9900078699503, (1, 2185): 862.9984992526752, (1, 2186): 862.2968604546131, (1, 2190): 864.3008682300098, (1, 2192): 863.0207548028128, (1, 2193): 863.2728629702494, (1, 2194): 861.9646599501618, (1, 2195): 861.6707278916386, (1, 2197): 863.2494317985016, (1, 2205): 861.2696829528793, (1, 2207): 858.7262068208116, (1, 2208): 860.1276388680395, (1, 2212): 863.8831215805535, (1, 2214): 835.5707735707941, (1, 2225): 838.4147050446087, (1, 2231): 834.4568511548562, (1, 2278): 850.7713356011226, (1, 2284): 853.2842078532285, (1, 2285): 852.8274424515765, (1, 2291): 846.9285977423492, (1, 2292): 848.1503159002439, (1, 2307): 851.510476671015, (1, 2313): 846.0920089122382, (1, 2317): 846.4059910020479, (1, 2319): 849.0184513120053, (1, 2321): 850.1550524555785, (1, 2323): 850.1699372180271, (1, 2326): 855.2271449102118, (1, 2327): 854.0574793186705, (1, 2329): 853.2408951421014, (1, 2330): 852.268925605148, (1, 2332): 854.1124875501233, (1, 2344): 851.3841927241706, (1, 2346): 851.2064584597424, (1, 2361): 851.764485076202, (1, 2368): 864.8331758403746, (1, 2374): 866.0256845961763, (1, 2375): 866.5176114657751, (1, 2377): 862.1165541859663, (1, 2378): 867.2751646423543, (1, 2379): 867.263985864116, (1, 2380): 867.7953569456141, (1, 2383): 863.388693127096, (1, 2385): 864.1244483338985, (1, 2395): 864.3100430195476, (1, 2397): 866.6743389938728, (1, 2398): 860.700761268727, (1, 2399): 862.370168299213, (1, 2400): 862.0110959220211, (1, 2402): 864.2249336928037, (1, 2403): 865.2173251390456, (1, 2404): 865.5241886891126, (1, 2405): 863.0864854919299, (1, 2407): 865.1463989004508, (1, 2408): 866.2581787380509, (1, 2409): 863.8454241842452, (1, 2411): 865.0009307896391, (1, 2412): 864.8191762427767, (1, 2413): 865.6045170620279, (1, 2414): 864.2524123304192, (1, 2422): 864.6253423266414, (1, 2424): 865.1452541702296, (1, 2426): 865.4028633459877, (1, 2433): 863.4692464868671, (1, 2436): 862.8390249644532, (1, 2437): 857.0751085397136, (1, 2440): 858.3828550432208, (1, 2445): 882.8718758876594, (1, 2447): 879.8450064696174, (1, 2454): 882.8190521302072, (1, 2455): 883.0927327454157, (1, 2460): 873.7131351284412, (1, 2461): 874.8471270365717, (1, 2471): 892.6709231953798, (1, 2492): 868.4670444853775, (1, 2511): 860.0286871372667, (1, 2523): 864.3290220312189, (1, 2525): 862.6652037463931, (1, 2535): 867.63360343218, (1, 2537): 865.5072077401182, (1, 2538): 867.0965060096568, (1, 2539): 865.8904648753479, (1, 2540): 868.5829009348591, (1, 2542): 869.9110594476167, (1, 2559): 900.5302867873562, (1, 2575): 897.1535924611874, (1, 2599): 854.3353200420156, (1, 2600): 863.9055795333136, (1, 2607): 858.8205577454564, (1, 2627): 863.4595817229593, (1, 2647): 868.433576096325, (1, 2674): 866.3636667727166, (1, 2681): 865.262172892192, (1, 2683): 868.0672693563992, (1, 2686): 865.1943919488152, (1, 2689): 900.2141639481746, (1, 2690): 900.3010123274207, (1, 2713): 904.5671170839477, (1, 2714): 904.808251101844, (1, 2715): 905.6953002087189, (1, 2739): 905.0126917615004, (1, 2740): 900.3964862561561, (1, 2741): 900.9063168353308, (1, 2749): 903.4157702902967, (1, 2750): 903.8184508902795, (1, 2752): 904.5076383090001, (1, 2755): 905.1292309371592, (1, 2758): 904.8190450841994, (1, 2759): 904.878577334932, (1, 2769): 903.9923257803894, (1, 2771): 901.5736523378006, (1, 2779): 900.9426275637853, (1, 2784): 890.5930426670787, (1, 2800): 891.4688035453016, (1, 2802): 898.2025449229031, (1, 2803): 897.9787738528775, (1, 2804): 897.4325650397278, (1, 2805): 898.6064406080335, (1, 2807): 898.6656685142297, (1, 2809): 898.0811598416554, (1, 2812): 892.6994774426527, (1, 2814): 897.0216659606824, (1, 2817): 896.1790922872839, (1, 2819): 899.0603454737882, (1, 2823): 892.2594298416028, (1, 2832): 899.5423866875253, (1, 2836): 895.579368323739, (1, 2839): 898.7688082355774, (1, 2841): 896.9024579629771, (1, 2843): 896.7931633121743, (1, 2846): 895.8982240542275, (1, 2849): 899.9671956146937, (1, 2852): 899.1406069436276, (1, 2853): 900.3405595041814, (1, 2876): 900.2044091608628, (1, 2877): 903.3040974958495, (1, 2885): 903.1610238658391, (1, 2918): 900.2336175660173, (1, 2921): 901.4665584580436, (1, 2925): 896.0328042576022, (1, 2926): 894.4156209068171, (1, 2930): 897.4801629375106, (1, 2931): 896.3193269705258, (1, 2938): 900.0558325615018, (1, 2940): 904.9381202878706, (1, 2947): 900.5133324495825, (1, 2949): 897.8809380132733, (1, 2950): 898.3036598690172, (1, 2952): 897.6241245061495, (1, 2958): 897.571562040264, (1, 2959): 898.4422793762445, (1, 2960): 899.8694953608846, (1, 2961): 899.0613014478358, (1, 2963): 896.889791321213, (1, 2968): 897.2047096125385, (1, 2976): 896.8266515725461, (1, 2981): 882.6018042716317, (1, 2982): 882.0003370289166, (1, 2984): 881.2776222777078, (1, 3003): 879.8454719083146, (1, 3046): 873.6702484561688, (1, 3050): 879.3430231514479, (1, 3051): 879.9589932371346, (1, 3053): 878.3859237967417, (1, 3069): 886.2705631799632, (1, 3071): 878.5448889190606, (1, 3080): 902.7826621722011, (1, 3199): 876.2410995832223, (1, 3200): 874.5171781537292, (1, 3205): 884.3088119015442, (1, 3209): 875.3096233759244, (1, 3215): 874.7419339119183, (1, 3217): 872.7774658590088, (1, 3249): 875.0547873079579, (1, 3263): 889.9462529237962, (1, 3289): 880.0992338357482, (1, 3301): 880.2416938082245, (1, 3302): 879.6552041900699, (1, 3307): 878.8081057370349, (1, 3310): 881.0870222393257, (1, 3391): 876.3470544010984, (1, 3509): 573.4457461430175, (1, 3510): 572.0799334064181, (1, 3511): 573.1612085797639, (1, 3512): 572.4664205894287, (1, 3514): 572.8891094272917, (1, 3519): 575.8081314057767, (1, 3536): 576.1573947962324, (1, 3545): 578.4740511348049, (1, 3548): 576.6018681171803, (1, 3572): 576.7253171491675, (1, 3581): 574.4974150439007, (1, 3583): 574.2740015330263, (1, 3601): 578.1071476016464, (1, 3656): 575.2263392037273, (1, 3669): 571.1133936665624, (1, 3670): 572.2771779629138, (1, 3695): 565.8837240606193, (1, 3696): 566.876653834863, (1, 3782): 580.0038088412272, (1, 3792): 578.0647017259082, (1, 3989): 28.01765468858509, (1, 4008): 30.797601848641925, (1, 4031): 26.875697091046575, (1, 4045): 29.217392677223657, (1, 4144): 33.39531864543753, (1, 4145): 36.888843506230735, (1, 4164): 33.695730191086156, (1, 4168): 35.57702435142812, (1, 4173): 36.69384260329572, (1, 4181): 36.52322242069789, (1, 4228): 31.331866637256024, (1, 4248): 39.241959500147225, (1, 4254): 83.08130311192606, (1, 4260): 80.71906041219518, (1, 4262): 80.35991185454014, (1, 4273): 79.29177474998593, (1, 4319): 109.5035283708458, (1, 4326): 109.67738686487462, (1, 4328): 108.81740419751377, (1, 4334): 109.25486106771113, (1, 4335): 110.1408695773925, (1, 4372): 342.88291239902577, (1, 4413): 357.3541261984135, (1, 4434): 340.8725412535745, (1, 4447): 336.73769232436837, (1, 4452): 341.7905470667165, (1, 4463): 362.08486617152215, (1, 4465): 360.4134793286415, (1, 4619): 374.5969941615987, (1, 4645): 372.6175993734376, (1, 4657): 374.5642903015635, (1, 4666): 376.1683282426082, (1, 4676): 376.49942551347584, (1, 4678): 375.61636941862736, (1, 4689): 377.7899347253776, (1, 4704): 380.1866337273665, (1, 4726): 431.5466224942271, (1, 4727): 430.7601177912058, (1, 4730): 429.1047865818172, (1, 4731): 430.4513656451846, (1, 4734): 426.318724477036, (1, 4735): 426.3268626101914, (1, 4736): 427.3554054131497, (1, 4737): 426.92449077675, (1, 4738): 427.6279249560349, (1, 4756): 428.81267449377134, (1, 4760): 421.20445943602033, (1, 4761): 420.1651502153698, (1, 4762): 421.0368644954073, (1, 4765): 422.0314020824199, (1, 4773): 432.36943078441124, (1, 4774): 432.8675768790865, (1, 4790): 431.66619133036653, (1, 4795): 430.67799575535196, (1, 4799): 433.84282388456705, (1, 4801): 437.12972271298725, (1, 4804): 429.44096560268895, (1, 4805): 428.64635657641514, (1, 4806): 434.3371127841374, (1, 4815): 434.6389555791013, (1, 4816): 436.061506524657, (1, 4817): 437.82785581876806, (1, 4826): 436.2324793262538, (1, 4830): 435.70596232236767, (1, 4839): 423.54877657931615, (1, 4840): 424.8443372672303, (1, 4841): 423.6831924186074, (1, 4846): 422.90695701917446, (1, 4848): 423.93298249117873, (1, 4850): 424.84610098737306, (1, 4871): 410.3315609378055, (1, 4883): 418.57151602032366, (1, 4900): 412.6242182860778, (1, 4901): 412.6291701757696, (1, 4917): 398.0927362947053, (1, 4931): 394.6495653814537, (1, 4944): 397.5972049937081, (1, 4956): 396.1638354808546, (1, 4958): 397.8224625152989, (1, 4959): 398.37951652462453, (1, 4961): 396.1387810246121, (1, 4966): 396.35066895170354, (1, 5207): 392.82607421627523, (1, 5272): 289.90461778966255, (1, 5283): 290.8902709475506, (1, 5287): 296.73408155117573, (1, 5289): 297.3499515566202, (1, 5293): 285.95076362561696, (1, 5295): 288.1420514823545, (1, 5296): 290.7112521755505, (1, 5298): 292.12531963670114, (1, 5303): 295.0222780797593, (1, 5305): 294.452926261934, (1, 5306): 297.4983070017052, (1, 5307): 294.27303919222453, (1, 5308): 295.6503045107739, (1, 5313): 292.36970077275055, (1, 5314): 291.8903683786378, (1, 5317): 297.33539464861235, (1, 5319): 294.84501758852264, (1, 5324): 292.4090307974993, (1, 5326): 290.6957303700629, (1, 5348): 299.5317289138127, (1, 5351): 303.70533836131887, (1, 5399): 301.6014100977376, (1, 5413): 310.4180426674523, (1, 5422): 299.4905393559312, (1, 5445): 298.7666461078962, (1, 5448): 298.0611244844509, (1, 5456): 300.6253089948957, (1, 5467): 302.00708808821275, (1, 5624): 286.7242469485602, (1, 5671): 276.40797115268765, (1, 5672): 274.62945757929464, (1, 5797): 297.9057699313265, (1, 5871): 338.3864475420044, (1, 5976): 328.88916546323713, (1, 6118): 727.2061282030166, (1, 6248): 752.6659100384409, (1, 6345): 256.8898843202322, (1, 6352): 262.8286520603334, (1, 6354): 255.60461547832423, (1, 6359): 254.16385632153163, (1, 6376): 261.28255436087915, (1, 6378): 256.2700646463654, (1, 6381): 254.45495774142856, (1, 6383): 258.2516340061948, (1, 6396): 254.11327947276644, (1, 6399): 256.4922226153404, (1, 6408): 262.86839085544216, (1, 6409): 260.8090867524618, (1, 6419): 271.46542087412695, (1, 6422): 262.6462183749686, (1, 6423): 263.1627902825045, (1, 6424): 257.0364967930996, (1, 6439): 258.40696921415946, (1, 6464): 260.2651853104467, (1, 6465): 260.5813220878975, (1, 6469): 259.3033193695355, (1, 6470): 259.54100869541713, (1, 6472): 252.06226791953796, (1, 6480): 254.55973160144225, (1, 6486): 252.66614029372283, (1, 6497): 253.34310431873476, (1, 6503): 261.5336901382795, (1, 6508): 260.2127059754193, (1, 6509): 259.5138922475503, (1, 6521): 254.44955764171388, (1, 6544): 255.7315253874797, (1, 6552): 262.9911759422986, (1, 6553): 263.9797711367667, (1, 6554): 264.9749395185632, (1, 6578): 261.2189154134158, (1, 6582): 262.81645387207146, (1, 6601): 260.9518848480432, (1, 6609): 252.29630862984823, (1, 6610): 252.20313010186277, (1, 6611): 251.5505544043613, (1, 6614): 251.78561393508397, (1, 6615): 251.76253790110422, (1, 6616): 251.35865978848327, (1, 6617): 251.58299237380302, (1, 6618): 250.80090381985826, (1, 6619): 252.5758262976481, (1, 6620): 251.63626785084654, (1, 6621): 252.51168883615767, (1, 6622): 252.1138998908468, (1, 6623): 252.1764528135659, (1, 6624): 253.20298873044229, (1, 6625): 253.203130600225, (1, 6626): 252.5024559758103, (1, 6627): 251.75136729003697, (1, 6628): 252.1156089081199, (1, 6629): 253.33377334540518, (1, 6630): 253.4661022239133, (1, 6632): 253.25426044822316, (1, 6634): 254.5284655317794, (1, 6635): 252.64288309845784, (1, 6636): 251.4153245773832, (1, 6637): 254.48698933692225, (1, 6638): 253.62598041030404, (1, 6639): 251.82359037711137, (1, 6640): 253.3485691809256, (1, 6641): 252.7705934920119, (1, 6642): 253.79281163639877, (1, 6643): 252.40415066283182, (1, 6645): 252.5865184554211, (1, 6646): 250.85448045673706, (1, 6647): 253.44195021781198, (1, 6653): 251.71435461715535, (1, 6655): 251.72629748515806, (1, 6658): 254.69649740834433, (1, 6662): 254.04306059437468, (1, 6819): 304.6697822928467, (1, 6996): 293.88245057433045, (1, 7059): 283.08180597978384, (1, 7187): 316.88048262372, (1, 7304): 329.90387513078497, (1, 7528): 300.836524262718, (1, 7720): 233.55930226378888, (1, 7793): 237.83949631118708, (1, 7807): 236.00771239782088, (1, 7808): 238.86618677020925, (1, 7831): 248.54772260074716, (1, 7850): 236.4963586074914, (1, 7852): 238.43478563044454, (1, 8012): 232.56206836835912, (1, 8125): 248.08238008059263, (1, 8208): 215.86355200592484, (1, 8392): 247.1046944268234, (1, 8651): 358.92310125658935, (1, 9088): 304.2894277096624, (1, 9443): 400.549283115091, (1, 9444): 399.3330823761015, (1, 9828): 456.9540068653108, (1, 9868): 450.1638590717383, (1, 10180): 249.20985888137253, (1, 10256): 230.11836201258427, (1, 10276): 234.81085275177676, (1, 10378): 220.41228146129467, (1, 10676): 275.02114298212933, (1, 10714): 293.67681518733184, (1, 10730): 277.4780899111971, (1, 10862): 446.61570741149234, (1, 10881): 445.957333987614, (1, 10883): 446.7402984895349, (1, 10885): 446.58357840578446, (1, 10891): 447.9752565599228, (1, 10909): 446.33851121135234, (1, 10911): 444.50679995959, (1, 10913): 445.2204388698506, (1, 10915): 444.33084746157664, (1, 10919): 443.48542734958005, (1, 11037): 469.55885856836426, (1, 11039): 464.2828006319808, (1, 11516): 102.41842640269714, (1, 11856): 108.99157525085758, (1, 11857): 112.55975306314924, (1, 11861): 110.82699059155593, (1, 11881): 107.38172432737653, (1, 11902): 109.59727360076992, (1, 11911): 107.13006944206103, (1, 11914): 108.056155500029, (1, 11922): 107.38047214957786, (1, 11924): 106.10139318734836, (1, 11926): 106.55951840272262, (1, 11950): 102.04667812033834, (1, 11963): 100.5411031986077, (1, 11983): 96.48966853705721, (1, 11985): 100.14731204904207, (1, 12009): 95.82139504093159, (1, 12010): 98.03830808494763, (1, 12018): 97.23877107483959, (1, 12020): 97.58556859914512, (1, 12021): 96.90049997342854, (1, 12024): 95.88755482824017, (1, 12025): 97.16279840006372, (1, 12027): 97.1645138289077, (1, 12031): 98.2614118031128, (1, 12032): 98.58970491945483, (1, 12035): 94.83722496864793, (1, 12041): 102.79311724167444, (1, 12045): 119.74056891950454, (1, 12145): 103.65021566733591, (1, 12275): 24.0, (1, 12294): 24.0, (1, 12358): 36.03777577627268, (1, 12463): 46.4646381241129, (1, 12465): 46.17803781101157, (1, 12482): 50.72889069359241, (1, 12503): 50.03448141868514, (1, 12506): 51.28750065218309, (1, 12549): 49.107496888757225, (1, 12559): 47.96676605353936, (1, 12569): 48.78615013002191, (1, 12572): 49.747797712922726, (1, 12574): 47.79445298006902, (1, 12576): 50.336915003460014, (1, 12591): 50.82832418605245, (1, 12608): 59.34688862030307, (1, 12696): 47.53378080813224, (1, 12710): 56.605541039741304, (1, 12728): 51.173438988019356, (1, 12766): 156.45385771835168, (1, 12771): 165.32994876415344, (1, 12790): 166.57635752340124, (1, 12795): 169.45768796443855, (1, 12797): 181.52976509098553, (1, 12798): 179.89939035432658, (1, 12811): 170.30483017500015, (1, 12830): 173.46359061002383, (1, 12848): 171.93478367710253, (1, 12850): 171.27259784629894, (1, 12852): 173.94974641672414, (1, 12854): 175.41977462867612, (1, 12859): 170.52901795664295, (1, 12861): 178.3099653890393, (1, 12865): 168.45394962115273, (1, 12866): 169.2384317386762, (1, 12867): 166.27001779966122, (1, 12874): 167.70442410574924, (1, 12875): 166.6051974103217, (1, 12881): 171.13296258957897, (1, 12883): 169.3192664003085, (1, 12885): 165.63374130232074, (1, 12888): 170.17790607522113, (1, 12889): 170.60987809621204, (1, 12892): 167.37979706116397, (1, 12893): 170.09364098817497, (1, 12896): 169.2359508584158, (1, 12906): 167.57303965485974, (1, 13018): 182.2047002735753, (1, 13071): 182.7943061061236, (1, 13131): 192.4821770870935, (1, 13146): 182.76616746814594, (1, 13159): 198.12185103408243, (1, 13193): 194.3151118043924, (1, 13198): 211.30141848196737, (1, 13292): 191.95035472031455, (1, 13296): 187.08286691919068, (1, 13406): 221.81987526608484, (1, 13407): 222.41052380056666, (1, 13417): 224.18842379144493, (1, 13418): 222.4898529569799, (1, 13438): 214.61515199526252, (1, 13442): 213.00859527169771, (1, 13443): 214.44695745444338, (1, 13764): 346.1560017026496, (1, 13766): 344.2983602586693, (1, 13771): 346.76026923505464, (1, 13783): 346.687686311708, (1, 13784): 342.0008455694037, (1, 13792): 351.36757748291853, (1, 13824): 348.0806277498722, (1, 14017): 334.1980781503415, (1, 14870): 410.65124872418147, (1, 14997): 325.8600487404601, (1, 15000): 326.2432455560396, (1, 15003): 325.69847303608884, (1, 15006): 320.81160075623615, (1, 15007): 319.7479964923059, (1, 15056): 321.5396591005365, (1, 15063): 322.8612301602696, (1, 15069): 323.8755492118621, (1, 15076): 319.95514221973497, (1, 15086): 322.78434205182486, (1, 15087): 324.73618446689926, (1, 15111): 327.5799913731498, (1, 15116): 325.9971937918297, (1, 15722): 355.63083390397225, (1, 15998): 389.43194178150827, (1, 16073): 609.9629750254705, (1, 16939): 788.9262330583741, (1, 16940): 787.2008918085165, (1, 16951): 788.7629746908373, (1, 16963): 789.0283848176109, (1, 16965): 791.305058637062, (1, 16969): 790.5421849657242, (1, 16970): 789.9307488175197, (1, 16971): 787.8942038993544, (1, 16973): 787.6127284560522, (1, 16974): 792.0815577055007, (1, 16976): 790.1800191881107, (1, 16978): 788.7427446554992, (1, 16980): 791.0552599492598, (1, 16982): 791.9144403610318, (1, 17045): 840.8695257112116, (1, 17048): 843.4044480515614, (1, 17304): 49.083197569957164, (1, 17305): 45.86151042944865, (1, 17330): 46.7113505773404, (1, 17334): 50.168776241613756, (1, 17343): 45.72144298834957, (1, 17345): 46.59111240861643, (1, 17347): 44.38510436430206, (1, 17351): 50.98430038101316, (1, 17372): 48.86497896660651, (1, 17373): 46.29805572699956, (1, 17377): 45.83221191515192, (1, 17382): 46.68845721203556, (1, 17383): 47.73097068395999, (1, 17389): 47.994051348821934, (1, 17400): 47.66557173764944, (1, 17401): 48.25988183423175, (1, 17402): 47.26587341314834, (1, 17403): 46.88991454434404, (1, 17440): 42.66126235439484, (1, 17455): 43.465182446915435, (1, 17491): 40.71131413415333, (1, 17507): 59.12576251677758, (1, 17509): 59.68029563656412, (1, 17590): 47.41839691782724, (1, 17615): 73.20177823948588, (1, 17642): 70.85200183262181, (1, 17643): 69.53442936489465, (1, 17668): 74.08248641959304, (1, 17721): 83.15192413660925, (1, 17754): 81.42942392579644, (1, 17769): 63.171153326750236, (1, 17776): 58.346186513398116, (1, 17804): 63.3327413298845, (1, 17809): 63.09589983186751, (1, 17824): 65.59646862614424, (1, 17837): 55.6571869869128, (1, 17838): 53.581733703651885, (1, 17862): 52.94422111247867, (1, 17866): 53.039289610479365, (1, 17872): 54.499019204352045, (1, 17873): 54.17494835316227, (1, 17881): 54.43255757358958, (1, 17947): 649.5092046767154, (1, 17951): 645.9650365148028, (1, 17953): 645.374256328141, (1, 17954): 645.6786424329827, (1, 17959): 648.6326891297346, (1, 17963): 647.2323071081873, (1, 18000): 629.4445192683777, (1, 18001): 630.272046227032, (1, 18111): 683.6490094295087, (1, 18148): 595.3467273954791, (1, 18166): 630.0084709657244, (1, 18189): 661.3313225692474, (1, 18239): 47.55430590468444, (1, 18240): 47.146030929398435, (1, 18245): 47.31982231536017, (1, 18247): 46.934020504727194, (1, 18251): 46.8202975846531, (1, 18256): 46.22046284748407, (1, 18258): 46.04125047865028, (1, 18259): 45.80936752268428, (1, 18260): 45.47714695538483, (1, 18262): 45.148971383936036, (1, 18263): 45.971613603652465, (1, 18264): 45.66852456802173, (1, 18266): 44.76657023940751, (1, 18267): 44.528117616289975, (1, 18268): 44.257567762550444, (1, 18269): 43.73998802741828, (1, 18275): 43.98213869343367, (1, 18285): 45.93378870170299, (1, 18308): 51.43665339976442, (1, 18313): 52.17577294646468, (1, 18314): 50.56068695256674, (1, 18315): 44.90335762866688, (1, 18316): 44.38158059392837, (1, 18317): 44.10528462080519, (1, 18320): 44.64352506106787, (1, 18321): 44.243151866499645, (1, 18322): 43.92140442553475, (1, 18324): 44.44677813033495, (1, 18325): 44.22199976507347, (1, 18326): 44.32995878419348, (1, 18327): 43.392251434451914, (1, 18329): 44.742158162155995, (1, 18330): 43.13222552673471, (1, 18331): 43.55406136965461, (1, 18332): 43.708544656723745, (1, 18333): 43.64611408807067, (1, 18336): 44.59767851598974, (1, 18337): 44.873981210958725, (1, 18403): 41.891469610651605, (1, 18432): 31.210468419665574, (1, 18451): 37.851750172634425, (1, 18466): 47.760915630147665, (1, 18481): 46.3035523012478, (1, 18483): 45.91323771880875, (1, 18484): 46.343485735369065, (1, 18485): 48.04968281880149, (1, 18486): 49.08362040084881, (1, 18487): 49.87105683858609, (1, 18489): 47.79062757298876, (1, 18490): 48.55624227532957, (1, 18491): 48.42163114393324, (1, 18492): 49.86869654227842, (1, 18493): 49.603726171784054, (1, 18494): 47.53271829238787, (1, 18495): 48.71775048473843, (1, 18496): 48.542671424149795, (1, 18497): 50.41771307423697, (1, 18498): 48.74626751740338, (1, 18499): 48.368603053041085, (1, 18501): 49.33474463563029, (1, 18502): 49.62349155840716, (1, 18503): 49.369455365184415, (1, 18504): 47.99933757680792, (1, 18506): 50.42942882532408, (1, 18507): 50.92738119136164, (1, 18508): 48.801769838602276, (1, 18509): 49.16989395978365, (1, 18510): 49.91140023469044, (1, 18511): 50.33706419451105, (1, 18512): 49.86579492865313, (1, 18515): 48.53559846390177, (1, 18516): 49.81236854103297, (1, 18517): 50.731901351958875, (1, 18518): 49.278076891636786, (1, 18519): 47.72307754518544, (1, 18520): 48.402272899766416, (1, 18522): 46.03864079948222, (1, 18523): 46.43089876090837, (1, 18532): 46.79592751129177, (1, 18535): 46.48741142823162, (1, 18537): 46.33005701996722, (1, 18539): 46.585980362037915, (1, 18540): 46.840920673922376, (1, 18541): 47.11517265221834, (1, 18542): 47.24985175628395, (1, 18543): 46.76678137391652, (1, 18546): 47.72215833080189, (1, 18555): 48.022185399791496, (1, 18556): 48.37306029038135, (1, 18565): 47.35459256260649, (1, 18567): 48.29609355833451, (1, 18568): 47.757468170070354, (1, 18577): 48.9923878989601, (1, 18583): 47.57130499040897, (1, 18605): 46.436421862648224, (1, 18608): 50.123990803111845, (1, 18616): 48.003662183720536, (1, 18618): 50.31184087226144, (1, 18625): 46.63368576207184, (1, 18645): 44.03609923963723, (1, 18646): 45.39340308718449, (1, 18653): 47.27779872860412, (1, 18654): 48.48100463104749, (1, 18655): 48.32234908658193, (1, 18666): 48.463676209654516, (1, 18837): 24.0, (1, 18974): 28.320707352668485, (1, 18999): 24.0, (1, 19000): 24.0, (1, 19174): 50.84836176212824, (1, 19342): 33.54542035292728, (1, 19455): 43.81757247917754, (1, 19555): 91.37162921793951, (1, 19564): 89.54908916670088, (1, 19573): 91.31193318740053, (1, 19586): 92.03734454384305, (1, 19605): 91.05655934309253, (1, 19611): 89.74187381356526, (1, 19614): 90.07626550294741, (1, 19641): 66.82603203574115, (1, 19702): 67.90940438082286, (1, 19713): 69.39667171703628, (1, 19731): 100.27204362584042, (1, 19819): 49.73341100633238, (1, 19893): 200.51381312346325, (1, 19899): 206.2217305063355, (1, 19929): 199.58286207913878, (1, 19951): 203.59872572489255, (1, 19962): 204.22891833202718, (1, 19970): 195.79987799295608, (1, 19971): 197.9183828972108, (1, 19972): 199.20652036732852, (1, 19975): 197.63049155692278, (1, 19978): 194.87863666437636, (1, 19987): 193.49800377397827, (1, 19989): 192.17831784498833, (1, 20039): 193.0493737509399, (1, 20043): 191.6346840820854, (1, 20047): 189.35587392925288, (1, 20052): 189.54671170404475, (1, 20054): 190.60293236110587, (1, 20085): 185.3896224766935, (1, 20104): 185.62034405577865, (1, 20132): 186.6315399831417, (1, 20203): 219.51566464818853, (1, 20280): 225.48439521816087, (1, 20285): 228.0247470454074, (1, 20290): 224.35747767278718, (1, 20297): 223.7502576987075, (1, 20309): 210.76124413603762, (1, 20453): 205.1768172426059, (1, 20485): 221.22714853566757, (1, 20520): 220.0466513601093, (1, 20526): 226.2235012874903, (1, 20698): 411.66800455596234, (1, 20868): 477.74141414572665, (1, 21042): 183.6532623381366, (1, 21057): 170.79996341170707, (1, 21066): 178.3284042325371, (1, 21075): 178.9795124661813, (1, 21093): 184.38610189385972, (1, 21098): 178.05067991356236, (1, 21127): 183.4898665395778, (1, 21130): 181.9279446960883, (1, 21144): 180.6687184418743, (1, 21146): 184.31745814978356, (1, 21147): 180.4122402009804, (1, 21148): 178.74553151614347, (1, 21153): 178.4933569666142, (1, 21293): 164.89369793136044, (1, 21426): 155.04893459925373, (1, 21442): 139.5932439141624, (1, 21451): 138.14966509553398, (1, 21466): 147.76438908146793, (1, 21469): 145.87865066945545, (1, 21471): 148.7051773396472, (1, 21473): 147.24641157415894, (1, 21475): 148.66328211090095, (1, 21482): 144.34292487087114, (1, 21484): 144.91656136910277, (1, 21488): 145.93045626460105, (1, 21494): 149.16268002292335, (1, 21498): 147.6372796908032, (1, 21500): 150.45596076929436, (1, 21514): 148.6734062376983, (1, 21537): 152.11255205225137, (1, 21662): 148.74628485357113, (1, 21691): 156.29806021848566, (1, 21757): 165.83095702708016, (1, 21777): 213.4932263077743, (1, 21778): 215.32120057565427, (1, 21779): 215.1487111851788, (1, 21790): 210.52557869844549, (1, 21802): 212.2882708280908, (1, 21824): 211.2802520931129, (1, 21874): 215.743184202283, (1, 21879): 218.43966490609554, (1, 21983): 202.2563920125414, (1, 22002): 188.60661454850242, (1, 22132): 184.27873486759663, (1, 22261): 485.47943547737486, (1, 22298): 482.33934939642506, (1, 22339): 508.63347817377615, (1, 22508): 445.5096770061283, (1, 22841): 851.5526914187868, (1, 22842): 851.7682378355618, (1, 22874): 847.5738606643955, (1, 22941): 847.3769831988906, (1, 22956): 850.5457656470508, (1, 22960): 850.9347476590125, (1, 22968): 856.6635129519328, (1, 22970): 857.0897341899116, (1, 22974): 860.2801691361966, (1, 22980): 863.8968416657625, (1, 23025): 865.9415006258504, (1, 23028): 865.6236837726518, (1, 23081): 874.5984972124312, (1, 23104): 871.9161234265961, (1, 23147): 833.4654290415493, (1, 23298): 120.37031638554002, (1, 23376): 125.91177339075786, (1, 23381): 133.64679760138367, (1, 23529): 120.68350570771238, (1, 23556): 123.18175937014207, (1, 23718): 120.43585451890232, (1, 24001): 87.40413094860413, (1, 24094): 88.60548218329608, (1, 24129): 84.1888294463874, (1, 24174): 98.038988100866, (1, 24235): 91.9053932035609, (1, 24259): 84.75012971484544, (1, 24260): 85.55175406033945, (1, 24261): 85.89549094987012, (1, 24305): 78.99090059745771, (1, 24306): 79.02009616015295, (1, 24307): 79.6511863156944, (1, 24308): 68.65533668891936, (1, 24498): 59.23499864438876, (1, 24499): 59.429823628566155, (1, 24500): 59.75891506782905, (1, 24668): 51.947186548261676, (1, 24711): 62.0005637936031, (1, 24756): 65.98121724873215, (1, 24788): 63.09160154882393, (1, 24809): 70.90750502610892, (1, 24813): 67.97641535220073, (1, 24821): 68.72590892423683, (1, 24825): 69.08602973588124, (1, 24832): 70.72013401315942, (1, 24833): 70.03113775863972, (1, 24835): 69.63146656685554, (1, 24837): 67.91635037490944, (1, 24840): 71.15913327996833, (1, 24841): 69.40764893417129, (1, 24844): 71.57722118639848, (1, 24845): 69.19161327483317, (1, 24846): 71.73006517298315, (1, 24849): 71.57813100063771, (1, 24850): 68.32417186413856, (1, 24863): 75.4059977820246, (1, 24866): 73.83797556537981, (1, 24885): 73.61988415180353, (1, 24886): 74.43744570018724, (1, 24889): 68.10357553779089, (1, 24903): 65.48347918946533, (1, 24909): 68.31601060973307, (1, 24999): 46.682691917640476, (1, 25019): 43.57462464703574, (1, 25028): 46.2778425000606, (1, 25137): 251.20666524318023, (1, 25145): 250.21730846737933, (1, 25208): 264.6131782140968, (1, 25233): 266.2972530742419, (1, 25371): 235.74753013311556, (1, 25377): 233.98462304902543, (1, 25828): 291.90350254393235, (1, 25851): 296.61844276806477, (1, 25874): 287.3135020251412, (1, 25898): 289.79940529913006, (1, 25946): 292.63166229745156, (1, 26047): 285.5919561151759, (1, 26066): 222.7294612286486, (1, 26197): 256.9237410728497, (1, 26212): 354.7592108079345, (1, 26253): 361.09047619278874, (1, 26254): 358.1812989212862, (1, 26257): 357.56151429102357, (1, 26258): 360.2788152627943, (1, 26260): 358.76152067136223, (1, 26266): 357.5706233953941, (1, 26267): 356.32072054141133, (1, 26271): 356.7027295805154, (1, 26304): 332.84218038285616, (1, 26305): 331.8693907843596, (1, 26363): 304.74437400665585, (1, 26441): 503.460359515232, (1, 26442): 502.75617586800473, (1, 26450): 499.52779231770137, (1, 26459): 499.4429748497302, (1, 26462): 499.9681658167692, (1, 26467): 509.4708467542711, (1, 26471): 506.7229956976248, (1, 26472): 506.4161540792066, (1, 26473): 506.28291208600626, (1, 26476): 504.5145271278517, (1, 26485): 500.97243631312153, (1, 26493): 500.98479982121637, (1, 26524): 501.4674129446024, (1, 26525): 501.049475474094, (1, 26556): 505.4459655718417, (1, 26560): 505.269819329618, (1, 26561): 503.2477191527331, (1, 26564): 504.53129537582214, (1, 26569): 502.70269436946523, (1, 26570): 501.8332414348256, (1, 26573): 502.2855753404043, (1, 26581): 502.1510892248206, (1, 26583): 501.47856186113535, (1, 26593): 502.0983606577771, (1, 26837): 510.05523700045694, (1, 26844): 512.2535267443761, (1, 26863): 507.32325189061527, (1, 26893): 513.5919070568283, (1, 26902): 516.5724956645669, (1, 26905): 513.6832789001832, (1, 26912): 515.9692427952722, (1, 26921): 510.33488408851593, (1, 26922): 504.1545410842317, (1, 27212): 526.9745819380944, (1, 27218): 524.3686313844725, (1, 27239): 531.1893401751407, (1, 27257): 528.9729988255323, (1, 27274): 532.0367347626809, (1, 27279): 531.5443337359525, (1, 27282): 529.0580896324334, (1, 27283): 530.0813805970926, (1, 27285): 533.1496345908724, (1, 27286): 530.8326855448017, (1, 27290): 526.9292030776649, (1, 27295): 525.4296149876127, (1, 27300): 532.4739760426926, (1, 27344): 525.7176103988332, (1, 27366): 528.5094812140743, (1, 27383): 533.320029808264, (1, 27398): 536.4069919915764, (1, 27406): 533.9499773693275, (1, 27407): 534.7011657602533, (1, 27426): 531.5725198620662, (1, 27432): 520.7765166338563, (1, 27460): 527.5557965459524, (1, 27523): 528.9306742446976, (1, 27545): 573.4672408250855, (1, 27602): 629.8034203887453, (1, 27606): 630.8583571914756, (1, 27646): 571.4489327295864, (1, 27667): 582.7218472307236, (1, 27672): 583.3328406600216, (1, 27674): 581.3990635830214, (1, 27688): 583.0852105305961, (1, 27692): 585.2595213757257, (1, 27693): 583.5680718764811, (1, 27705): 583.4564152986499, (1, 27712): 584.2684025582307, (1, 27786): 632.3592851172067, (1, 27790): 625.802579304597, (1, 27791): 625.2339009195048, (1, 27795): 629.1910554445565, (1, 27801): 624.3333693573514, (1, 27813): 634.1206871127082, (1, 27816): 632.0269128501922, (1, 27823): 624.147034914511, (1, 27830): 629.4879381877637, (1, 27884): 552.4004480172422, (1, 27885): 566.6800835203854, (1, 27896): 558.0641789314594, (1, 27919): 557.4945705249693, (1, 27922): 559.2375911397913, (1, 27930): 554.6036775721997, (1, 27934): 555.1296489682228, (1, 27935): 555.5092392070726, (1, 27948): 623.0528977757025, (1, 27951): 626.5993553104109, (1, 28061): 562.537203447004, (1, 28290): 683.1769761312894, (1, 28292): 685.1392402114109, (1, 28293): 683.521468420016, (1, 28295): 682.1871383723112, (1, 28296): 682.8902447939382, (1, 28297): 682.0982123388123, (1, 28302): 680.9596421415382, (1, 28310): 690.841583839399, (1, 28313): 691.5989718385164, (1, 28372): 693.9813711341394, (1, 28398): 694.0187242476098, (1, 28399): 693.1116411789275, (1, 28400): 694.3159712779262, (1, 28401): 691.4120819599374, (1, 28445): 689.8202082405211, (1, 28475): 690.4147727576111, (1, 28885): 113.34746318840175, (1, 28886): 114.84356529067615, (1, 28915): 118.13561903005056, (1, 28916): 117.3886916558089, (1, 28917): 118.5056192134562, (1, 28921): 111.49239351241698, (1, 28931): 112.6442848382297, (1, 28945): 128.13532672525463, (1, 28982): 123.22960125813137, (1, 29219): 141.74148195170602, (1, 29228): 142.54555349619633, (1, 29246): 151.7456673526918, (1, 29248): 156.04125735503473, (1, 29282): 154.32176950864604, (1, 29290): 147.73662793504286, (1, 29291): 148.74369843861862, (1, 29292): 148.42060697140195, (1, 29293): 147.89486183918814, (1, 29294): 150.142328233236, (1, 29298): 149.07184358148055, (1, 29299): 150.18563106047975, (1, 29304): 147.1866564959778, (1, 29317): 144.74949165077783, (1, 29323): 144.4451387175639, (1, 29330): 145.76545215145782, (1, 29331): 145.49059954731007, (1, 29344): 149.9604802295357, (1, 29445): 182.03610611729889, (1, 29724): 833.5467843355176, (1, 29738): 834.5273690406943, (1, 29745): 831.2880880094451, (1, 29748): 829.9264608625216, (1, 29750): 830.7143635224321, (1, 29759): 828.8195071869893, (1, 29772): 832.4112997912086, (1, 29781): 831.5716256544185, (1, 29784): 831.7836887797808, (1, 29790): 832.0137180449346, (1, 29811): 829.1113144576252, (1, 29817): 830.6742371570142, (1, 29818): 829.8226170816437, (1, 29929): 832.1411437418303, (1, 30039): 850.1710052772894, (1, 30066): 844.9022896599364, (1, 30116): 807.577787554697, (1, 30238): 752.6240851659743, (1, 30248): 785.0082577474383, (1, 30260): 786.0853779792598, (1, 30545): 110.08268940415404, (1, 30733): 142.0373618229964, (1, 30756): 165.81200523766478, (1, 30921): 141.19429920405298, (1, 31079): 250.20879308687867, (1, 31149): 253.94146957370344, (1, 31154): 254.21613098744257, (1, 31160): 254.28526283567064, (1, 31163): 255.0171368595529, (1, 31189): 275.5729136299118, (1, 31215): 274.617486516558, (1, 31259): 278.967616277475, (1, 31262): 281.03043387714155, (1, 31430): 250.24530016450194, (1, 31568): 311.85653172390136, (1, 31751): 262.6361336951184, (3, 109): 46.90181432371211, (3, 872): 560.3458331736499, (3, 873): 562.9040039373045, (3, 877): 562.277804596117, (3, 879): 562.6897331397481, (3, 884): 560.8677830660981, (3, 889): 562.311546618086, (3, 891): 559.931903884146, (3, 892): 564.6036088407805, (3, 894): 564.1441780236661, (3, 896): 561.1259548369759, (3, 903): 562.755078917893, (3, 909): 557.3052074870217, (3, 910): 558.0202945005192, (3, 912): 556.4013054010973, (3, 913): 554.7315013484035, (3, 916): 553.5724473766626, (3, 926): 558.4534890371312, (3, 927): 557.5256653103812, (3, 948): 558.9511109106057, (3, 961): 559.0843811405874, (3, 962): 559.159047657493, (3, 963): 559.3126363219088, (3, 967): 563.7008270597181, (3, 974): 563.1087116465676, (3, 998): 564.9873626747165, (3, 1014): 616.9528162956709, (3, 1086): 545.1034739389071, (3, 1087): 543.6838328110299, (3, 1089): 541.9053723043301, (3, 1090): 543.0706145109328, (3, 1092): 546.749691019961, (3, 1097): 544.1603060240657, (3, 1107): 547.8877516412728, (3, 1387): 164.26109376625504, (3, 1554): 136.32379391589132, (3, 1827): 683.9419398440793, (3, 1828): 684.0709991703408, (3, 1829): 684.5606784545711, (3, 1830): 684.8256437080406, (3, 1831): 684.9357387288916, (3, 1832): 684.5954497925662, (3, 1833): 684.5113161485934, (3, 1836): 684.0867482329121, (3, 1841): 685.8960563779627, (3, 1843): 685.2088201525738, (3, 1844): 685.6288538866795, (3, 1845): 684.910934263948, (3, 1847): 681.9248127932898, (3, 1848): 682.8783997844537, (3, 1849): 687.4608064167245, (3, 1850): 687.8227069210894, (3, 1851): 683.9140427021488, (3, 1852): 684.2483265420394, (3, 1854): 684.4950724970248, (3, 1856): 682.140852851765, (3, 1857): 682.9582745515039, (3, 1858): 686.8427666567985, (3, 1861): 684.7293220633919, (3, 1866): 682.3098754064135, (3, 1867): 685.7196330538394, (3, 1868): 684.950893842142, (3, 1870): 685.8949827544363, (3, 1871): 685.371632821919, (3, 1875): 684.2678014470245, (3, 1880): 682.4960554328399, (3, 1882): 683.1544120711852, (3, 1883): 687.5575807788467, (3, 1889): 682.5432241784689, (3, 1893): 684.1774890012564, (3, 1894): 683.4490438325535, (3, 1899): 681.7856308863477, (3, 1900): 682.1758918118202, (3, 1902): 685.3099213883987, (3, 1905): 686.3253836372311, (3, 1907): 683.2395688895211, (3, 1910): 683.2217765750579, (3, 1917): 687.2306825272682, (3, 1920): 683.0685440682155, (3, 1935): 685.9299925797357, (3, 1937): 686.7342450196144, (3, 1946): 679.7346329502649, (3, 1949): 680.3921714790908, (3, 1950): 678.2797884806589, (3, 1951): 679.4459148368579, (3, 1952): 681.140044752039, (3, 1953): 680.9390108121081, (3, 1954): 680.7736626757131, (3, 1958): 680.4548689288014, (3, 1960): 681.9709648341144, (3, 1968): 682.5676171450758, (3, 1969): 685.5775444082578, (3, 1974): 684.8368473928232, (3, 1975): 685.0001804321324, (3, 1979): 682.7717626260801, (3, 1980): 683.1446375141136, (3, 1981): 683.3676460631481, (3, 1985): 683.6764193467927, (3, 1994): 678.4078549799254, (3, 2011): 683.2986816582047, (3, 2019): 690.643421935771, (3, 2020): 689.6763248062383, (3, 2029): 686.5119202234949, (3, 2030): 688.9977921936261, (3, 2032): 686.2573924233378, (3, 2033): 687.6812897285159, (3, 2034): 687.9083609556018, (3, 2036): 685.7237196411282, (3, 2037): 686.2414628832086, (3, 2038): 685.3163717094757, (3, 2042): 695.644627229204, (3, 2050): 686.8425496718153, (3, 2051): 686.9705916302797, (3, 2053): 687.123051895797, (3, 2054): 688.0462951896712, (3, 2066): 686.2162531497088, (3, 2067): 686.0803019962361, (3, 2071): 676.5500128599577, (3, 2072): 678.0395958369617, (3, 2073): 672.6750480806729, (3, 2074): 672.622617900102, (3, 2080): 670.2111984181864, (3, 2082): 678.9052979134234, (3, 2083): 679.6588730505655, (3, 2089): 677.6149535895815, (3, 2090): 678.2706414444025, (3, 2092): 677.0099858813068, (3, 2098): 670.9434903653743, (3, 2099): 672.0875109291568, (3, 2101): 671.0115978515624, (3, 2102): 675.2698604779919, (3, 2103): 674.0306907518601, (3, 2104): 673.4692158794776, (3, 2106): 680.3531792889311, (3, 2112): 671.8069130231418, (3, 2113): 676.0274289565009, (3, 2114): 677.4798129498254, (3, 2117): 681.2112939186555, (3, 2123): 665.1038426072521, (3, 2124): 665.9823873907128, (3, 2134): 664.1378781153502, (3, 2138): 666.4591308367003, (3, 2141): 664.2395771260146, (3, 2148): 668.0800074072308, (3, 2150): 662.2239182297512, (3, 2151): 663.3359897141526, (3, 2152): 661.9124173060042, (3, 2153): 668.1328743484669, (3, 2154): 664.3327373763465, (3, 2155): 664.3463650629606, (3, 2156): 663.3595252281117, (3, 2157): 665.862054687019, (3, 2160): 668.9176755739999, (3, 2161): 662.0147312834578, (3, 2162): 669.2555817128693, (3, 2163): 667.9353015848536, (3, 2164): 668.0081744320448, (3, 2168): 663.8913845053283, (3, 2172): 665.8856166368805, (3, 2174): 663.5514909941538, (3, 2178): 666.9510274991036, (3, 2179): 666.4796950473443, (3, 2183): 666.6946412796194, (3, 2185): 666.9079496132038, (3, 2186): 666.1227616849951, (3, 2190): 668.810597015699, (3, 2192): 667.4513738007859, (3, 2193): 666.852673805941, (3, 2194): 665.4653392804811, (3, 2195): 665.6036328706947, (3, 2197): 667.9147466173832, (3, 2205): 666.4528705524806, (3, 2207): 664.4446369924777, (3, 2208): 665.635390235818, (3, 2212): 666.5154495560847, (3, 2214): 644.6494169360259, (3, 2225): 648.8440872735911, (3, 2231): 635.2365469891214, (3, 2278): 664.4766358227215, (3, 2284): 667.813624313358, (3, 2285): 667.6473053620385, (3, 2291): 663.6015130475952, (3, 2292): 662.4118403488953, (3, 2307): 666.0455126364881, (3, 2313): 663.5068307953334, (3, 2317): 659.6267291487828, (3, 2319): 663.5483443148809, (3, 2321): 665.1257920175174, (3, 2323): 664.4530605893887, (3, 2326): 668.4031394297745, (3, 2327): 667.1909201137506, (3, 2329): 666.4154251433266, (3, 2330): 665.6506689452268, (3, 2332): 667.8833859308079, (3, 2344): 664.0691579556416, (3, 2346): 664.3637427671084, (3, 2361): 660.9611142917023, (3, 2368): 676.7939316385435, (3, 2374): 678.4002051818087, (3, 2375): 678.6730784319926, (3, 2377): 673.7406043619154, (3, 2378): 679.6663325500881, (3, 2379): 680.1355032198063, (3, 2380): 680.3492524790039, (3, 2383): 674.77628356112, (3, 2385): 675.3772231497652, (3, 2395): 675.1462692980163, (3, 2397): 679.7364880921147, (3, 2398): 672.2080384519892, (3, 2399): 673.7373136154004, (3, 2400): 673.3505878363155, (3, 2402): 677.0181859858188, (3, 2403): 678.0949102888752, (3, 2404): 678.2287625728469, (3, 2405): 675.7630282935039, (3, 2407): 677.5636450872618, (3, 2408): 678.9758983374983, (3, 2409): 676.4561812018591, (3, 2411): 678.6692837248759, (3, 2412): 678.1684935712572, (3, 2413): 679.1315355386896, (3, 2414): 677.7750140084147, (3, 2422): 678.5446674254802, (3, 2424): 678.344618794331, (3, 2426): 678.4593405466381, (3, 2433): 676.6856928112799, (3, 2436): 676.5349756588929, (3, 2437): 670.1663841041244, (3, 2440): 671.4658619505698, (3, 2445): 702.2486568919054, (3, 2447): 698.5250503146091, (3, 2454): 701.712151142575, (3, 2455): 701.6143528906767, (3, 2460): 692.0848778889651, (3, 2461): 693.321211544876, (3, 2471): 714.5540427633962, (3, 2492): 704.3550522668933, (3, 2511): 692.7953342379889, (3, 2523): 698.747095350996, (3, 2525): 697.8484591065276, (3, 2535): 694.778495261539, (3, 2537): 692.7930332855487, (3, 2538): 693.893571909803, (3, 2539): 694.5945739631587, (3, 2540): 695.7132053078798, (3, 2542): 697.6154184308533, (3, 2559): 725.092251473176, (3, 2575): 723.9316454816363, (3, 2599): 674.4717735653478, (3, 2600): 685.6015808685801, (3, 2607): 678.1461239607795, (3, 2627): 703.4837705782189, (3, 2647): 710.0599369252506, (3, 2674): 705.7150686366837, (3, 2681): 705.6175848041233, (3, 2683): 708.0777460658735, (3, 2686): 704.5589595212721, (3, 2689): 742.1865429725146, (3, 2690): 742.5323583825482, (3, 2713): 754.6491827971493, (3, 2714): 755.9466590470386, (3, 2715): 756.8225655042992, (3, 2739): 755.8465679727917, (3, 2740): 748.4337249927669, (3, 2741): 748.7364013276641, (3, 2749): 755.3470680230643, (3, 2750): 755.3818292454844, (3, 2752): 755.8983562296362, (3, 2755): 756.7437633185709, (3, 2758): 756.742720369612, (3, 2759): 756.6380056001955, (3, 2769): 755.3446459164887, (3, 2771): 750.3426402880782, (3, 2779): 752.3661133305515, (3, 2784): 743.1937699206859, (3, 2800): 746.6962382274763, (3, 2802): 747.6620998486349, (3, 2803): 747.1069309873037, (3, 2804): 746.4298516190597, (3, 2805): 749.0682222642954, (3, 2807): 748.7909995161484, (3, 2809): 748.9576847052197, (3, 2812): 742.7220992286951, (3, 2814): 750.1272552306132, (3, 2817): 752.3027917983039, (3, 2819): 748.3626690510075, (3, 2823): 745.1922095660723, (3, 2832): 750.4810532724838, (3, 2836): 746.4657984898391, (3, 2839): 748.5530074881509, (3, 2841): 751.4964493521248, (3, 2843): 750.8445902149994, (3, 2846): 748.1530360714826, (3, 2849): 751.4814559475752, (3, 2852): 750.4279055765418, (3, 2853): 751.9800239546868, (3, 2876): 753.417410771022, (3, 2877): 756.789564792293, (3, 2885): 759.858045752578, (3, 2918): 747.3957964300236, (3, 2921): 749.0504395393241, (3, 2925): 740.5613523102869, (3, 2926): 737.3102465454552, (3, 2930): 745.7906332430947, (3, 2931): 741.7780609320286, (3, 2938): 747.8006982874457, (3, 2940): 750.0173516616387, (3, 2947): 744.7733047146381, (3, 2949): 744.8724987427922, (3, 2950): 745.8797145225394, (3, 2952): 745.2032017003488, (3, 2958): 744.912041298069, (3, 2959): 745.1333105582569, (3, 2960): 746.8134234759788, (3, 2961): 746.2524594530844, (3, 2963): 744.5504814017462, (3, 2968): 745.2149731706487, (3, 2976): 744.1358261939833, (3, 2981): 733.8606416916097, (3, 2982): 733.9437927108006, (3, 2984): 733.3757984458381, (3, 3003): 732.6990660239035, (3, 3046): 718.6585302316436, (3, 3050): 728.0675278937043, (3, 3051): 728.4257762462388, (3, 3053): 727.1326026723931, (3, 3069): 736.1915441869286, (3, 3071): 725.7276772289428, (3, 3080): 760.633021553838, (3, 3199): 733.2973145103012, (3, 3200): 732.0540696130369, (3, 3205): 741.3590737407926, (3, 3209): 732.9165262253857, (3, 3215): 731.8968987826828, (3, 3217): 730.0568546019693, (3, 3249): 731.7980262014356, (3, 3263): 745.5875709768784, (3, 3289): 735.4719169207343, (3, 3301): 736.5725806923393, (3, 3302): 735.6666911560033, (3, 3307): 734.7702779575594, (3, 3310): 737.3657839366709, (3, 3391): 751.6194690135615, (3, 3509): 425.6693972855917, (3, 3510): 424.3560472782702, (3, 3511): 424.83452683226943, (3, 3512): 423.67486361883607, (3, 3514): 423.63695078334223, (3, 3519): 430.6843387914153, (3, 3536): 427.29145001801777, (3, 3545): 428.9563227442921, (3, 3548): 426.4228401135169, (3, 3572): 428.5178012716014, (3, 3581): 428.2441224968034, (3, 3583): 425.7216737162383, (3, 3601): 433.7623653828484, (3, 3656): 433.14486228386016, (3, 3669): 433.86144628885484, (3, 3670): 435.17475772112215, (3, 3695): 427.09416115174196, (3, 3696): 427.96314582403147, (3, 3782): 420.0649264447681, (3, 3792): 419.6557807911915, (3, 3989): 293.82007077917416, (3, 4008): 301.171379956261, (3, 4031): 303.68406366090636, (3, 4045): 298.2234987077297, (3, 4144): 295.8142942857614, (3, 4145): 285.3515180124063, (3, 4164): 292.246523184646, (3, 4168): 288.5156973143003, (3, 4173): 287.33101797444147, (3, 4181): 282.85352940220343, (3, 4228): 281.90590744719856, (3, 4248): 275.6437978778401, (3, 4254): 221.5204401769519, (3, 4260): 223.23345142130856, (3, 4262): 224.7950996267346, (3, 4273): 225.23405369500475, (3, 4319): 192.40751211753397, (3, 4326): 191.96826424833876, (3, 4328): 192.75054077366607, (3, 4334): 193.00079543111244, (3, 4335): 192.09665088974526, (3, 4372): 103.08776137729757, (3, 4413): 128.56081431258627, (3, 4434): 101.42617526078514, (3, 4447): 102.48782069039025, (3, 4452): 102.08103904868577, (3, 4463): 79.95213395900318, (3, 4465): 79.51961108252327, (3, 4619): 138.29769925967884, (3, 4645): 141.36773275986323, (3, 4657): 141.60963045116893, (3, 4666): 140.8149733202883, (3, 4676): 143.72302238149567, (3, 4678): 143.9418767448515, (3, 4689): 143.05953388388943, (3, 4704): 157.93846619461925, (3, 4726): 212.29980984299817, (3, 4727): 211.3768910414835, (3, 4730): 209.52879850982984, (3, 4731): 210.4426875989671, (3, 4734): 209.29123127366123, (3, 4735): 208.7378277672637, (3, 4736): 209.4577665594025, (3, 4737): 208.28938702412563, (3, 4738): 208.7245305416643, (3, 4756): 209.82090811299108, (3, 4760): 203.62192607361945, (3, 4761): 203.52647729806915, (3, 4762): 202.73962859551895, (3, 4765): 204.2615420213793, (3, 4773): 213.7978084145752, (3, 4774): 213.48740658818124, (3, 4790): 213.10863258487083, (3, 4795): 212.1757831181086, (3, 4799): 214.1594431433733, (3, 4801): 216.80346865053306, (3, 4804): 211.85736961469703, (3, 4805): 211.10007675834632, (3, 4806): 213.9010032720877, (3, 4815): 213.47727281160803, (3, 4816): 215.55003442984503, (3, 4817): 216.61266541265945, (3, 4826): 215.04939424562684, (3, 4830): 213.99797259529873, (3, 4839): 206.3330011321295, (3, 4840): 207.400407021648, (3, 4841): 205.66045871675587, (3, 4846): 204.92484668733667, (3, 4848): 205.2145874066703, (3, 4850): 206.13712939024094, (3, 4871): 193.22153705066464, (3, 4883): 201.87391656154975, (3, 4900): 196.75263788231604, (3, 4901): 195.98827783450443, (3, 4917): 149.3702001262763, (3, 4931): 143.4860965237986, (3, 4944): 149.56733774812332, (3, 4956): 145.04519708077137, (3, 4958): 145.83944218346153, (3, 4959): 145.40058313090012, (3, 4961): 145.84509684702056, (3, 4966): 144.1722887991724, (3, 5207): 137.818612312858, (3, 5272): 24.0, (3, 5283): 24.0, (3, 5287): 24.0, (3, 5289): 24.0, (3, 5293): 24.0, (3, 5295): 24.0, (3, 5296): 24.0, (3, 5298): 24.0, (3, 5303): 24.0, (3, 5305): 24.0, (3, 5306): 24.0, (3, 5307): 24.0, (3, 5308): 24.0, (3, 5313): 24.0, (3, 5314): 24.0, (3, 5317): 24.0, (3, 5319): 24.0, (3, 5324): 24.0, (3, 5326): 24.0, (3, 5348): 24.0, (3, 5351): 24.0, (3, 5399): 24.0, (3, 5413): 24.0, (3, 5422): 24.0, (3, 5445): 24.0, (3, 5448): 24.0, (3, 5456): 24.0, (3, 5467): 24.0, (3, 5624): 27.484140677398987, (3, 5671): 48.789793783319716, (3, 5672): 46.894291895316755, (3, 5797): 78.8553611561098, (3, 5871): 53.21920470285715, (3, 5976): 32.92455150834571, (3, 6118): 613.6629494402904, (3, 6248): 651.5187895434341, (3, 6345): 215.53223442615797, (3, 6352): 220.57475510164133, (3, 6354): 213.61204456787453, (3, 6359): 213.8815244101781, (3, 6376): 222.79681818363875, (3, 6378): 214.34604692030732, (3, 6381): 215.15778452565888, (3, 6383): 216.09631067951452, (3, 6396): 220.68404729310726, (3, 6399): 216.97487998711316, (3, 6408): 219.15418344494, (3, 6409): 213.49181738829608, (3, 6419): 216.75534907817385, (3, 6422): 215.91530238517427, (3, 6423): 216.1453632450014, (3, 6424): 210.39000904699282, (3, 6439): 210.28967046723855, (3, 6464): 210.66002437648075, (3, 6465): 212.29206455584026, (3, 6469): 214.04694187655895, (3, 6470): 214.90592943785336, (3, 6472): 212.70254607124488, (3, 6480): 208.20143530192396, (3, 6486): 199.38632239253184, (3, 6497): 202.0624362515759, (3, 6503): 203.7057882249078, (3, 6508): 206.9306584959125, (3, 6509): 204.31818294393125, (3, 6521): 205.10046426910347, (3, 6544): 201.96819246339408, (3, 6552): 209.21295161763587, (3, 6553): 209.64826675428853, (3, 6554): 210.14048426678184, (3, 6578): 208.99352045834223, (3, 6582): 205.8110901580002, (3, 6601): 208.03092185147594, (3, 6609): 207.70141785327317, (3, 6610): 206.7854247746472, (3, 6611): 208.6773749572079, (3, 6614): 210.13545560397475, (3, 6615): 209.34588017993664, (3, 6616): 206.21339567624207, (3, 6617): 207.36456679916614, (3, 6618): 203.96596861697574, (3, 6619): 210.11327507004737, (3, 6620): 204.9602226504259, (3, 6621): 205.15579952417855, (3, 6622): 205.909649496034, (3, 6623): 208.83343764816615, (3, 6624): 207.93874367492887, (3, 6625): 208.68984502151466, (3, 6626): 210.6778414123482, (3, 6627): 211.3256267269177, (3, 6628): 203.7877987116169, (3, 6629): 206.29424188963281, (3, 6630): 211.0561434907319, (3, 6632): 207.0277141894004, (3, 6634): 210.75644244101053, (3, 6635): 205.98799764178133, (3, 6636): 205.7581293289513, (3, 6637): 206.78258420987808, (3, 6638): 209.82712828251994, (3, 6639): 210.5581119918232, (3, 6640): 210.3749883619759, (3, 6641): 204.19598555195122, (3, 6642): 208.99498734189405, (3, 6643): 211.6080723779841, (3, 6645): 209.48870964294193, (3, 6646): 205.10636182626502, (3, 6647): 209.31487752924195, (3, 6653): 209.74730151609057, (3, 6655): 210.95469416417723, (3, 6658): 210.30917158664616, (3, 6662): 208.13861764126136, (3, 6819): 222.8902586186687, (3, 6996): 194.88795376713955, (3, 7059): 187.829417875326, (3, 7187): 166.15457237763587, (3, 7304): 203.56164830649803, (3, 7528): 179.8858003143867, (3, 7720): 156.85919049723293, (3, 7793): 150.19378056296952, (3, 7807): 152.1759344573339, (3, 7808): 148.66835418314784, (3, 7831): 195.938759774607, (3, 7850): 197.39968435384617, (3, 7852): 200.22885198356215, (3, 8012): 168.17531398290558, (3, 8125): 114.87633498753077, (3, 8208): 148.93642538611533, (3, 8392): 172.25482907968373, (3, 8651): 260.77056804431544, (3, 9088): 246.74432276415314, (3, 9443): 241.2735337594033, (3, 9444): 239.28323277250962, (3, 9828): 275.94274127627085, (3, 9868): 288.2179975627632, (3, 10180): 111.14993566504974, (3, 10256): 98.02159568445292, (3, 10276): 109.23006355471728, (3, 10378): 127.99230424081716, (3, 10676): 89.80759590290967, (3, 10714): 97.9309765782261, (3, 10730): 112.19806398934911, (3, 10862): 151.7873785289205, (3, 10881): 150.41158862747747, (3, 10883): 151.24893124498553, (3, 10885): 151.92727226525653, (3, 10891): 152.56732042114498, (3, 10909): 151.04326233291815, (3, 10911): 149.1672949386891, (3, 10913): 150.02751134000866, (3, 10915): 149.17516676231796, (3, 10919): 148.25386692315692, (3, 11037): 179.31735464929298, (3, 11039): 177.58106328046824, (3, 11516): 399.0909959835056, (3, 11856): 193.47879833278293, (3, 11857): 190.27714972128885, (3, 11861): 191.85282509846982, (3, 11881): 194.1121121953799, (3, 11902): 190.6851335756524, (3, 11911): 192.5170106169827, (3, 11914): 191.91616008654518, (3, 11922): 193.60175746299382, (3, 11924): 195.03283940305843, (3, 11926): 194.18646203314754, (3, 11950): 198.78864735899285, (3, 11963): 201.674377206113, (3, 11983): 203.8110527693281, (3, 11985): 202.9339260756042, (3, 12009): 205.9203256824722, (3, 12010): 202.96506703461398, (3, 12018): 203.7954187537801, (3, 12020): 203.83562584386522, (3, 12021): 204.57881908047622, (3, 12024): 206.5932421544405, (3, 12025): 205.1750922721978, (3, 12027): 204.87821945735902, (3, 12031): 202.5976049920276, (3, 12032): 202.71407615720162, (3, 12035): 206.61877622479062, (3, 12041): 201.10292117397788, (3, 12045): 179.51523662609358, (3, 12145): 194.3439818217099, (3, 12275): 303.20498757705064, (3, 12294): 301.3833124003477, (3, 12358): 323.34537053565754, (3, 12463): 334.5613591590912, (3, 12465): 334.5717767061481, (3, 12482): 334.38249634074924, (3, 12503): 334.7819043597252, (3, 12506): 335.56993531962746, (3, 12549): 329.8606059165266, (3, 12559): 330.0590619500229, (3, 12569): 332.12483680518204, (3, 12572): 332.63482812268927, (3, 12574): 331.127928879908, (3, 12576): 330.06415157594495, (3, 12591): 327.6280476932648, (3, 12608): 330.75292211834636, (3, 12696): 321.58472191735723, (3, 12710): 323.0281659056137, (3, 12728): 324.07915633870834, (3, 12766): 228.6261447553406, (3, 12771): 215.67002138466626, (3, 12790): 215.81630587555944, (3, 12795): 217.55388447932856, (3, 12797): 208.4734861355077, (3, 12798): 208.34310738607527, (3, 12811): 211.00228409467724, (3, 12830): 212.15397299386927, (3, 12848): 208.39797502238932, (3, 12850): 206.08023203604822, (3, 12852): 210.765800676158, (3, 12854): 210.39684413829312, (3, 12859): 207.67638675960305, (3, 12861): 207.7760683909381, (3, 12865): 213.3546166454122, (3, 12866): 211.90388866288575, (3, 12867): 213.84760817828067, (3, 12874): 213.0737336748671, (3, 12875): 212.85685085500032, (3, 12881): 213.0262524657179, (3, 12883): 213.37036129025924, (3, 12885): 213.41668578073896, (3, 12888): 212.32423950857046, (3, 12889): 211.40345717663783, (3, 12892): 213.6392624665658, (3, 12893): 213.1949093316493, (3, 12896): 212.56444669418056, (3, 12906): 216.8842019126478, (3, 13018): 236.0910614667049, (3, 13071): 241.02588650732707, (3, 13131): 219.77981433057906, (3, 13146): 216.91888305977918, (3, 13159): 240.81645124856658, (3, 13193): 218.13716618389722, (3, 13198): 209.02740122566294, (3, 13292): 207.63210469441438, (3, 13296): 199.32262823638786, (3, 13406): 223.05203683561123, (3, 13407): 224.1748182321206, (3, 13417): 232.88738655273082, (3, 13418): 234.18923752851998, (3, 13438): 227.0964213742704, (3, 13442): 224.15780233134015, (3, 13443): 224.5747016069219, (3, 13764): 319.61786884228553, (3, 13766): 318.61460453360957, (3, 13771): 322.3866866811209, (3, 13783): 315.8101492598093, (3, 13784): 316.3171386455311, (3, 13792): 328.5136828399728, (3, 13824): 317.0691036251067, (3, 14017): 294.8272203364001, (3, 14870): 117.83719809776838, (3, 14997): 170.3666688128939, (3, 15000): 168.950535436567, (3, 15003): 166.70081917484592, (3, 15006): 170.24869839814457, (3, 15007): 169.15440953469962, (3, 15056): 165.34581273987718, (3, 15063): 165.45659900466464, (3, 15069): 164.32349526367938, (3, 15076): 168.06596671379424, (3, 15086): 172.7716228305983, (3, 15087): 171.99532430617128, (3, 15111): 176.2247359691227, (3, 15116): 173.66381992253434, (3, 15722): 201.626135446358, (3, 15998): 196.14259939892256, (3, 16073): 537.910525339526, (3, 16939): 614.7019673271715, (3, 16940): 612.7779343654623, (3, 16951): 615.9343443817824, (3, 16963): 615.8805090146653, (3, 16965): 617.7967582062424, (3, 16969): 617.8355136415528, (3, 16970): 616.3863996075197, (3, 16971): 614.6246864547935, (3, 16973): 614.8549382158184, (3, 16974): 618.9006240657565, (3, 16976): 616.3026576067564, (3, 16978): 614.8933522940121, (3, 16980): 616.657841342142, (3, 16982): 619.2499143849108, (3, 17045): 703.2872638089078, (3, 17048): 705.7835055394586, (3, 17304): 261.3524498404841, (3, 17305): 262.4882387950386, (3, 17330): 262.7884242177901, (3, 17334): 258.95144475831427, (3, 17343): 264.73171832211597, (3, 17345): 261.1560885567338, (3, 17347): 264.1293401923685, (3, 17351): 256.22823068310214, (3, 17372): 259.58902284127095, (3, 17373): 264.2680918264026, (3, 17377): 264.78210085420017, (3, 17382): 262.2146885649671, (3, 17383): 261.9308839054578, (3, 17389): 260.60089897994726, (3, 17400): 262.8421183881765, (3, 17401): 262.4319209606145, (3, 17402): 263.2124467389263, (3, 17403): 263.6521989140095, (3, 17440): 263.7834480933673, (3, 17455): 265.77637420068356, (3, 17491): 267.69571559086114, (3, 17507): 252.16153242438622, (3, 17509): 252.93720841403245, (3, 17590): 257.89533118814137, (3, 17615): 235.75011762968714, (3, 17642): 238.24543171260888, (3, 17643): 239.0094725970691, (3, 17668): 235.14313214517736, (3, 17721): 227.01127787974067, (3, 17754): 238.43427081515068, (3, 17769): 250.03180832996543, (3, 17776): 248.86776559555526, (3, 17804): 251.81872916676738, (3, 17809): 253.16503410170765, (3, 17824): 250.870835871827, (3, 17837): 253.67752916641334, (3, 17838): 255.10594545659507, (3, 17862): 254.74178108077797, (3, 17866): 256.9378089728962, (3, 17872): 253.01630599708486, (3, 17873): 251.64801529264628, (3, 17881): 253.94579697189226, (3, 17947): 450.001676634774, (3, 17951): 447.3186239732801, (3, 17953): 446.4139279444925, (3, 17954): 446.34470631575044, (3, 17959): 450.12290653442614, (3, 17963): 449.86070184759416, (3, 18000): 435.17720553616874, (3, 18001): 435.17964840188813, (3, 18111): 459.71657572763735, (3, 18148): 381.56848758583317, (3, 18166): 409.4499651222045, (3, 18189): 440.0366800382165, (3, 18239): 264.0900092852977, (3, 18240): 264.3206537879229, (3, 18245): 264.342401215133, (3, 18247): 264.31294557200465, (3, 18251): 264.6374193577993, (3, 18256): 265.2764098286397, (3, 18258): 265.083913267769, (3, 18259): 265.2771013473633, (3, 18260): 265.5929126190716, (3, 18262): 266.01159088378347, (3, 18263): 265.5046923409073, (3, 18264): 265.80298249700394, (3, 18266): 266.3304221843954, (3, 18267): 266.5875086560313, (3, 18268): 266.80602491289005, (3, 18269): 267.34459096672185, (3, 18275): 267.0916218966848, (3, 18285): 265.60431940669463, (3, 18308): 259.94982634473524, (3, 18313): 258.7282587572409, (3, 18314): 260.0569212292026, (3, 18315): 266.63548818892235, (3, 18316): 266.92908776957876, (3, 18317): 267.20178628945695, (3, 18320): 266.980646234405, (3, 18321): 267.2794439078352, (3, 18322): 267.64198676459904, (3, 18324): 267.4670697773891, (3, 18325): 268.1370470130886, (3, 18326): 267.8722381327434, (3, 18327): 267.72745468382135, (3, 18329): 268.0706469271678, (3, 18330): 268.75965472780183, (3, 18331): 268.149574693344, (3, 18332): 267.6914290020486, (3, 18333): 268.39692407398655, (3, 18336): 267.528387711215, (3, 18337): 267.5458564658908, (3, 18403): 269.05876834817826, (3, 18432): 269.71289859154757, (3, 18451): 269.2896685847863, (3, 18466): 268.101699039756, (3, 18481): 265.93529942811676, (3, 18483): 266.16857336039345, (3, 18484): 265.6206098389178, (3, 18485): 263.7321957672944, (3, 18486): 263.88548135274687, (3, 18487): 262.7406394397217, (3, 18489): 264.57814292823286, (3, 18490): 264.79925520672305, (3, 18491): 265.20369457426375, (3, 18492): 262.0746070001049, (3, 18493): 263.4611071523937, (3, 18494): 264.6041881651195, (3, 18495): 264.46273817984496, (3, 18496): 264.2318911014388, (3, 18497): 262.25890504089097, (3, 18498): 263.41547989041334, (3, 18499): 264.1331834164025, (3, 18501): 263.1974229347875, (3, 18502): 262.7109021124447, (3, 18503): 262.6250281347718, (3, 18504): 264.68911775174547, (3, 18506): 262.5883316268378, (3, 18507): 261.989703941178, (3, 18508): 263.8047349617198, (3, 18509): 263.590425351272, (3, 18510): 262.30678291673803, (3, 18511): 263.11874311218276, (3, 18512): 263.0257482004813, (3, 18515): 264.3982939400221, (3, 18516): 263.6602499133207, (3, 18517): 262.70774165409125, (3, 18518): 264.24412070462216, (3, 18519): 264.92333187318957, (3, 18520): 263.9512630647484, (3, 18522): 267.30001001088783, (3, 18523): 267.1369945704132, (3, 18532): 267.377037290068, (3, 18535): 266.6156966827459, (3, 18537): 266.19282145270773, (3, 18539): 266.1469473388332, (3, 18540): 266.0542423042086, (3, 18541): 266.14532233991963, (3, 18542): 266.2277697990235, (3, 18543): 265.71410270300163, (3, 18546): 265.5211602236549, (3, 18555): 266.16223788288926, (3, 18556): 266.1042102383855, (3, 18565): 266.98222719074334, (3, 18567): 266.66659171647404, (3, 18568): 266.53123075542845, (3, 18577): 269.1708624774781, (3, 18583): 269.42874862437833, (3, 18605): 270.82908456799413, (3, 18608): 265.8656245584898, (3, 18616): 273.26069840383377, (3, 18618): 274.907336446754, (3, 18625): 276.0396762826751, (3, 18645): 274.95032864090615, (3, 18646): 274.819537119834, (3, 18653): 271.29427239473654, (3, 18654): 272.9037123282741, (3, 18655): 271.4619222705613, (3, 18666): 281.43707336677414, (3, 18837): 301.39243112905854, (3, 18974): 275.26750002092473, (3, 18999): 280.18019540428037, (3, 19000): 280.8633032927629, (3, 19174): 269.41085692423803, (3, 19342): 287.1267406919938, (3, 19455): 259.9235626812652, (3, 19555): 243.8692929167132, (3, 19564): 254.32239068326612, (3, 19573): 251.37796807085624, (3, 19586): 249.47470441138088, (3, 19605): 248.39808532179856, (3, 19611): 250.04509823154967, (3, 19614): 246.82263889400463, (3, 19641): 263.9610938891004, (3, 19702): 266.40888373362924, (3, 19713): 264.55045132480507, (3, 19731): 226.5435921979645, (3, 19819): 260.85047286736324, (3, 19893): 101.77871593140249, (3, 19899): 102.64370955151333, (3, 19929): 103.66200477882218, (3, 19951): 112.98329490428695, (3, 19962): 100.8343467814704, (3, 19970): 109.50900422047697, (3, 19971): 107.95232616061132, (3, 19972): 106.09581109332555, (3, 19975): 106.90531735433531, (3, 19978): 121.66200848571275, (3, 19987): 122.80571427328924, (3, 19989): 119.84436432504934, (3, 20039): 123.84041612783001, (3, 20043): 126.46515998237697, (3, 20047): 126.63604405741972, (3, 20052): 122.29852518411718, (3, 20054): 121.8892654662351, (3, 20085): 146.96227937912855, (3, 20104): 148.38430556271078, (3, 20132): 138.60738990569502, (3, 20203): 86.51731532722368, (3, 20280): 80.88189688867104, (3, 20285): 78.72799522488738, (3, 20290): 82.26053993388517, (3, 20297): 81.62721141136832, (3, 20309): 113.1777611055459, (3, 20453): 142.6272360676262, (3, 20485): 78.58601311182161, (3, 20520): 78.5379103071181, (3, 20526): 72.48994339131552, (3, 20698): 394.09483773529723, (3, 20868): 440.2646971646763, (3, 21042): 155.40555075000165, (3, 21057): 160.1380978750177, (3, 21066): 154.96383310343768, (3, 21075): 158.03146204151997, (3, 21093): 151.91782516389003, (3, 21098): 149.6346453226754, (3, 21127): 153.7286377075143, (3, 21130): 152.6785825785758, (3, 21144): 156.14396516606624, (3, 21146): 153.4753731386259, (3, 21147): 157.146029471552, (3, 21148): 156.64779295660261, (3, 21153): 168.86386553600974, (3, 21293): 158.66407172201016, (3, 21426): 191.30535593686108, (3, 21442): 203.3693218603135, (3, 21451): 204.41589657318187, (3, 21466): 195.44442354717336, (3, 21469): 195.60626891896624, (3, 21471): 195.4427408795486, (3, 21473): 195.1604892375075, (3, 21475): 194.96301848663498, (3, 21482): 197.06657747906468, (3, 21484): 196.31847628964633, (3, 21488): 196.5836738867047, (3, 21494): 193.08266253279172, (3, 21498): 193.6759843257914, (3, 21500): 191.25636692816138, (3, 21514): 185.44727227297122, (3, 21537): 186.94157192174197, (3, 21662): 181.07251058446636, (3, 21691): 178.74863546757967, (3, 21757): 189.73962284944048, (3, 21777): 138.197935730995, (3, 21778): 138.28021376644222, (3, 21779): 136.446741687866, (3, 21790): 140.07830848658304, (3, 21802): 136.5763727632504, (3, 21824): 134.77089229530648, (3, 21874): 134.23337561660674, (3, 21879): 131.015329204157, (3, 21983): 148.9984254836789, (3, 22002): 139.01689611340504, (3, 22132): 178.75337519478572, (3, 22261): 271.5051775949514, (3, 22298): 266.17138730832954, (3, 22339): 284.9869951558388, (3, 22508): 235.4972797353813, (3, 22841): 770.1813921248048, (3, 22842): 769.9958069640247, (3, 22874): 764.5054623745983, (3, 22941): 765.6659673562029, (3, 22956): 768.4405721674011, (3, 22960): 769.7775898539094, (3, 22968): 769.9826251014072, (3, 22970): 771.1823763590503, (3, 22974): 770.9091683379446, (3, 22980): 774.4240500168206, (3, 23025): 771.5458230260574, (3, 23028): 770.2335929917583, (3, 23081): 772.9469910804158, (3, 23104): 762.1069909694276, (3, 23147): 738.5131566751476, (3, 23298): 189.84075970680857, (3, 23376): 186.4082667253035, (3, 23381): 176.48373621414729, (3, 23529): 185.72635308837093, (3, 23556): 184.65328486159964, (3, 23718): 194.2632983457888, (3, 24001): 213.94666932629818, (3, 24094): 209.4629972894268, (3, 24129): 213.8035631831991, (3, 24174): 200.03778759455378, (3, 24235): 206.57942112575742, (3, 24259): 213.91757562988153, (3, 24260): 213.13033889520747, (3, 24261): 212.61275160329788, (3, 24305): 220.3338356639255, (3, 24306): 220.59951678826587, (3, 24307): 219.63274395435818, (3, 24308): 232.3113439960756, (3, 24498): 240.85879502195914, (3, 24499): 240.74502993602465, (3, 24500): 240.13116080683267, (3, 24668): 246.0885138998991, (3, 24711): 241.78107519595926, (3, 24756): 241.09269564407245, (3, 24788): 244.02761300487327, (3, 24809): 235.03043242743325, (3, 24813): 238.1567996075604, (3, 24821): 237.27484396416781, (3, 24825): 237.30278712216844, (3, 24832): 234.92156352550418, (3, 24833): 235.9335456396804, (3, 24835): 236.75297698995197, (3, 24837): 238.80895987356567, (3, 24840): 234.53607861541843, (3, 24841): 236.57327715804539, (3, 24844): 234.27239689104698, (3, 24845): 236.40398877441652, (3, 24846): 234.61526783839102, (3, 24849): 235.0198371565751, (3, 24850): 238.0891965392142, (3, 24863): 226.35707692671784, (3, 24866): 228.26025781044783, (3, 24885): 229.33271409962342, (3, 24886): 228.80721004057844, (3, 24889): 235.19363373890008, (3, 24903): 237.78949719649117, (3, 24909): 232.89881227323926, (3, 24999): 319.3222755637775, (3, 25019): 319.49280989163395, (3, 25028): 317.70578458445794, (3, 25137): 68.52555410241679, (3, 25145): 70.78256042233728, (3, 25208): 90.36367974729761, (3, 25233): 87.14084364100879, (3, 25371): 76.67862170688439, (3, 25377): 73.76190267856919, (3, 25828): 71.74995337751322, (3, 25851): 91.33820969784598, (3, 25874): 76.7652624868636, (3, 25898): 64.89214193319972, (3, 25946): 73.49815427084883, (3, 26047): 34.61191975528572, (3, 26066): 77.61385957580019, (3, 26197): 51.661455276341236, (3, 26212): 113.36440046571954, (3, 26253): 118.78526543286242, (3, 26254): 116.83233504746737, (3, 26257): 114.52409926630135, (3, 26258): 117.57481684991092, (3, 26260): 116.03404371470307, (3, 26266): 119.09129487101498, (3, 26267): 117.13000721073529, (3, 26271): 116.93362555088409, (3, 26304): 99.9284315186916, (3, 26305): 100.73004210532353, (3, 26363): 70.10555033246398, (3, 26441): 255.80351277635776, (3, 26442): 255.56179880143384, (3, 26450): 252.3693677975171, (3, 26459): 250.46205340631602, (3, 26462): 250.18234773692575, (3, 26467): 259.30938194722694, (3, 26471): 257.5652560581226, (3, 26472): 257.53506430848034, (3, 26473): 257.66336076499704, (3, 26476): 258.6448152446289, (3, 26485): 252.8275701926443, (3, 26493): 253.7771927292539, (3, 26524): 250.82425366053408, (3, 26525): 250.91034802285924, (3, 26556): 256.2530823583618, (3, 26560): 254.60063462952292, (3, 26561): 252.31296343592322, (3, 26564): 255.78391289415313, (3, 26569): 252.27710044934776, (3, 26570): 252.00955543282635, (3, 26573): 253.24206104697703, (3, 26581): 253.8267599774226, (3, 26583): 252.73936828839507, (3, 26593): 254.68535705921704, (3, 26837): 260.58330917463303, (3, 26844): 262.37170576159616, (3, 26863): 260.08594320214655, (3, 26893): 265.85127978416585, (3, 26902): 268.3310927972874, (3, 26905): 264.4083257671151, (3, 26912): 266.7959543746974, (3, 26921): 262.7457142996322, (3, 26922): 260.1635718325479, (3, 27212): 247.601692882885, (3, 27218): 244.16622020498662, (3, 27239): 251.83577224085758, (3, 27257): 250.05016627505495, (3, 27274): 252.83505348447835, (3, 27279): 252.73352463984884, (3, 27282): 250.33537050689057, (3, 27283): 250.60666236934884, (3, 27285): 254.12958929402774, (3, 27286): 252.5426407834189, (3, 27290): 248.3450871652448, (3, 27295): 246.34270941516723, (3, 27300): 253.11320586803262, (3, 27344): 248.29902404973163, (3, 27366): 251.3574767778589, (3, 27383): 255.07097014272813, (3, 27398): 257.1522496754129, (3, 27406): 254.51185672437455, (3, 27407): 254.9490455147611, (3, 27426): 249.5455891994516, (3, 27432): 239.80253899280208, (3, 27460): 245.59449196109418, (3, 27523): 258.1804666114717, (3, 27545): 294.1375300668943, (3, 27602): 351.77277761702527, (3, 27606): 352.42765127358746, (3, 27646): 300.90335237263713, (3, 27667): 312.10019838675527, (3, 27672): 312.4076918300371, (3, 27674): 310.67071801817264, (3, 27688): 311.17496725493004, (3, 27692): 314.66790221742485, (3, 27693): 313.04808831587076, (3, 27705): 313.2807475033487, (3, 27712): 314.34821355268633, (3, 27786): 345.7427730530001, (3, 27790): 336.74870637655073, (3, 27791): 335.8505697661626, (3, 27795): 342.7859285176185, (3, 27801): 336.28548400140517, (3, 27813): 347.80277009899436, (3, 27816): 345.1942597157905, (3, 27823): 336.01738040645847, (3, 27830): 342.07262405777135, (3, 27884): 285.8272188899279, (3, 27885): 296.7255628909022, (3, 27896): 289.9147832937941, (3, 27919): 289.1212690142932, (3, 27922): 290.96932747421863, (3, 27930): 287.0274490505137, (3, 27934): 287.74344499877964, (3, 27935): 288.39497483397787, (3, 27948): 359.52057833496025, (3, 27951): 357.86885016810754, (3, 28061): 353.8856415488104, (3, 28290): 453.0319401151409, (3, 28292): 456.6082426242358, (3, 28293): 453.8361710347968, (3, 28295): 453.7653124634081, (3, 28296): 453.378479616308, (3, 28297): 451.2276345863149, (3, 28302): 451.2148188616987, (3, 28310): 559.4866710524279, (3, 28313): 562.9955041038044, (3, 28372): 559.9385013313718, (3, 28398): 560.3730683308158, (3, 28399): 559.8482885946808, (3, 28400): 561.1406591106838, (3, 28401): 557.3233630474941, (3, 28445): 562.9080727095118, (3, 28475): 552.3448929618195, (3, 28885): 187.97263720624386, (3, 28886): 186.3741462872405, (3, 28915): 183.9667224308681, (3, 28916): 184.2641048194087, (3, 28917): 183.14127597247202, (3, 28921): 190.18429136854564, (3, 28931): 189.13372874310326, (3, 28945): 174.53935929787934, (3, 28982): 179.0165959638808, (3, 29219): 167.42506458934545, (3, 29228): 164.35824098586343, (3, 29246): 178.5057352993721, (3, 29248): 175.55978644602138, (3, 29282): 171.58201540206483, (3, 29290): 183.47624457999206, (3, 29291): 181.82641773363113, (3, 29292): 182.9929734277626, (3, 29293): 181.31049583081014, (3, 29294): 181.53111643021745, (3, 29298): 180.73593294077068, (3, 29299): 179.88193054632498, (3, 29304): 179.90072780812582, (3, 29317): 176.9640693590466, (3, 29323): 176.8273348464451, (3, 29330): 178.0855941570701, (3, 29331): 179.3366505196202, (3, 29344): 161.78631809507507, (3, 29445): 116.04502354340299, (3, 29724): 768.7126703599987, (3, 29738): 769.6384064445207, (3, 29745): 767.1796742771916, (3, 29748): 768.9356719161136, (3, 29750): 770.9622314219469, (3, 29759): 767.5160689309363, (3, 29772): 770.9594866070103, (3, 29781): 770.242720612821, (3, 29784): 769.1293114969575, (3, 29790): 771.2070348260715, (3, 29811): 769.7861584942387, (3, 29817): 779.2928054435569, (3, 29818): 778.6140511345083, (3, 29929): 766.0896175435968, (3, 30039): 774.6941871426407, (3, 30066): 764.8653861197337, (3, 30116): 736.099446331551, (3, 30238): 693.1828176954693, (3, 30248): 710.7131179198285, (3, 30260): 710.8730295166688, (3, 30545): 187.9084614801299, (3, 30733): 170.43573046803024, (3, 30756): 145.83939665710426, (3, 30921): 162.66025100286922, (3, 31079): 252.22943619531262, (3, 31149): 236.27265541002032, (3, 31154): 238.92070042821288, (3, 31160): 235.91396692761427, (3, 31163): 238.87640287656637, (3, 31189): 233.28711943198718, (3, 31215): 235.94200689593941, (3, 31259): 247.5558050881172, (3, 31262): 246.4308483372583, (3, 31430): 260.48833827146336, (3, 31568): 277.590411267113, (3, 31751): 256.68577672201457, (5, 109): 241.16472822636857, (5, 872): 705.8471910861183, (5, 873): 708.321327742437, (5, 877): 707.4385307860597, (5, 879): 707.8099497036842, (5, 884): 705.4252923445971, (5, 889): 706.9544093995722, (5, 891): 704.5945932328156, (5, 892): 709.7184298969935, (5, 894): 709.3875606745509, (5, 896): 706.9282249361102, (5, 903): 707.5830338441506, (5, 909): 703.2214057730062, (5, 910): 704.1698929778873, (5, 912): 702.5432140328243, (5, 913): 700.7664429070885, (5, 916): 699.9523288800453, (5, 926): 704.9257744680652, (5, 927): 704.0853460958166, (5, 948): 703.6905511069833, (5, 961): 704.9362353605916, (5, 962): 705.187607855264, (5, 963): 705.4796179980784, (5, 967): 708.6107024619363, (5, 974): 707.3882515159281, (5, 998): 709.6266637894521, (5, 1014): 763.1381635423634, (5, 1086): 698.4229277288481, (5, 1087): 697.9254495476803, (5, 1089): 695.7353486586275, (5, 1090): 696.7956932686161, (5, 1092): 700.3696403641657, (5, 1097): 697.68013491082, (5, 1107): 702.0314378869282, (5, 1387): 323.27792655452157, (5, 1554): 285.22840613972295, (5, 1827): 819.3461781936661, (5, 1828): 819.5985507757458, (5, 1829): 819.9837785775709, (5, 1830): 819.637569091286, (5, 1831): 819.8510595177125, (5, 1832): 819.5811107978469, (5, 1833): 819.6032782672837, (5, 1836): 819.3100867251476, (5, 1841): 820.9029064921646, (5, 1843): 820.2402942070934, (5, 1844): 820.5428433092931, (5, 1845): 819.7605419374935, (5, 1847): 817.1842116869756, (5, 1848): 818.0664465978925, (5, 1849): 822.2082034583444, (5, 1850): 822.6341934519864, (5, 1851): 818.7619414290406, (5, 1852): 818.8439618760455, (5, 1854): 819.252599953997, (5, 1856): 817.0823948837171, (5, 1857): 818.0159387676006, (5, 1858): 821.7942073227621, (5, 1861): 819.9435399143473, (5, 1866): 817.041365048636, (5, 1867): 820.9336378898082, (5, 1868): 820.3869680621364, (5, 1870): 820.4923410733661, (5, 1871): 820.798342182097, (5, 1875): 819.1959777718434, (5, 1880): 817.6187482639995, (5, 1882): 817.9046666288419, (5, 1883): 822.6483708587257, (5, 1889): 818.0492246382253, (5, 1893): 820.0018712303851, (5, 1894): 819.3737877286542, (5, 1899): 817.4874614170154, (5, 1900): 817.9400265337575, (5, 1902): 821.082329836671, (5, 1905): 821.8975337421734, (5, 1907): 818.6471163964937, (5, 1910): 818.9205803728884, (5, 1917): 823.5271506278144, (5, 1920): 818.6911478839475, (5, 1935): 821.9715927165157, (5, 1937): 822.6621754187634, (5, 1946): 816.0604239807111, (5, 1949): 816.8156048280318, (5, 1950): 814.1779133132499, (5, 1951): 815.4616933667709, (5, 1952): 816.4827183028103, (5, 1953): 816.8577801885777, (5, 1954): 816.2811940961444, (5, 1958): 816.6197018019722, (5, 1960): 817.9323517292046, (5, 1968): 818.4501859700719, (5, 1969): 822.0905653440213, (5, 1974): 821.1422340600651, (5, 1975): 821.1454324753901, (5, 1979): 819.2740975714365, (5, 1980): 819.1707125960213, (5, 1981): 819.6836913314066, (5, 1985): 820.1160868005628, (5, 1994): 813.2263979343343, (5, 2011): 817.8852129387121, (5, 2019): 824.3796741316604, (5, 2020): 823.5213362096107, (5, 2029): 820.2993247040496, (5, 2030): 822.9257673127576, (5, 2032): 819.7916926551391, (5, 2033): 821.4844946210657, (5, 2034): 821.4734759444145, (5, 2036): 818.3215404570982, (5, 2037): 819.1255829416514, (5, 2038): 819.3166164881006, (5, 2042): 829.1524631439053, (5, 2050): 821.0139374172139, (5, 2051): 820.8924997780177, (5, 2053): 821.1446241565516, (5, 2054): 822.0156647465379, (5, 2066): 820.2466802230898, (5, 2067): 820.241801634493, (5, 2071): 811.5737512089612, (5, 2072): 813.187407431855, (5, 2073): 808.6527986706113, (5, 2074): 808.4469762221556, (5, 2080): 805.7308443484619, (5, 2082): 814.0626887485151, (5, 2083): 814.8957056423569, (5, 2089): 813.0905315268507, (5, 2090): 813.8634698808593, (5, 2092): 812.7773654106093, (5, 2098): 806.7530423734111, (5, 2099): 807.7170432178717, (5, 2101): 806.6037749297324, (5, 2102): 811.0209943620297, (5, 2103): 809.6412236873454, (5, 2104): 808.8971679335008, (5, 2106): 815.4741427553862, (5, 2112): 807.2120055634781, (5, 2113): 811.663642952927, (5, 2114): 812.7672114408476, (5, 2117): 816.156584987243, (5, 2123): 808.6376193804531, (5, 2124): 809.5479001009603, (5, 2134): 807.0404295902023, (5, 2138): 809.684518029671, (5, 2141): 807.3294747895483, (5, 2148): 808.9847954293081, (5, 2150): 805.1298274086395, (5, 2151): 806.1123515144803, (5, 2152): 804.6491316225562, (5, 2153): 809.2622365258691, (5, 2154): 805.4701739026353, (5, 2155): 805.0889917344729, (5, 2156): 804.3491424736293, (5, 2157): 805.4965528945738, (5, 2160): 811.1165310364582, (5, 2161): 804.5249446332834, (5, 2162): 809.5388526420791, (5, 2163): 808.2494188083823, (5, 2164): 808.1824506249583, (5, 2168): 805.666431585436, (5, 2172): 806.6628253257719, (5, 2174): 806.0439176036889, (5, 2178): 807.4519964868667, (5, 2179): 806.8748212270724, (5, 2183): 809.6611012369357, (5, 2185): 809.7390972599331, (5, 2186): 809.0014853764219, (5, 2190): 811.2590920114816, (5, 2192): 809.9381790007084, (5, 2193): 809.9047294903272, (5, 2194): 808.5554495378477, (5, 2195): 808.4047591285641, (5, 2197): 810.2488636532971, (5, 2205): 808.4226945712383, (5, 2207): 806.0321019473921, (5, 2208): 807.3778484983785, (5, 2212): 810.2003240176331, (5, 2214): 783.741515631807, (5, 2225): 787.0734521282245, (5, 2231): 779.8198593186356, (5, 2278): 800.6787886391941, (5, 2284): 803.4986005992882, (5, 2285): 803.1340666986584, (5, 2291): 797.7866148490765, (5, 2292): 798.2134448350911, (5, 2307): 801.7056762787366, (5, 2313): 797.1886906515048, (5, 2317): 796.0985064531864, (5, 2319): 799.1821537208995, (5, 2321): 800.4804933271263, (5, 2323): 800.2644795899492, (5, 2326): 805.0091078808231, (5, 2327): 803.8113911222448, (5, 2329): 802.9990273257106, (5, 2330): 802.0853054507543, (5, 2332): 804.0815457269457, (5, 2344): 800.9557182091081, (5, 2346): 800.9347731637133, (5, 2361): 800.1657248271268, (5, 2368): 814.3165814505086, (5, 2374): 815.6622819555042, (5, 2375): 816.0858809928501, (5, 2377): 811.4553586998155, (5, 2378): 816.931583777185, (5, 2379): 817.0823741140381, (5, 2380): 817.5126009206463, (5, 2383): 812.6622444584704, (5, 2385): 813.360874399499, (5, 2395): 813.407970419839, (5, 2397): 816.5503226207652, (5, 2398): 809.9839639345415, (5, 2399): 811.6252064469181, (5, 2400): 811.2527041013517, (5, 2402): 813.9822167644976, (5, 2403): 815.0144098187735, (5, 2404): 815.2664215275361, (5, 2405): 812.7913565765431, (5, 2407): 814.7873907387728, (5, 2408): 816.0132197819959, (5, 2409): 813.5368144880707, (5, 2411): 815.0621893761063, (5, 2412): 814.7707826762307, (5, 2413): 815.6250506585174, (5, 2414): 814.2559296057882, (5, 2422): 814.7668837005731, (5, 2424): 815.0500354117022, (5, 2426): 815.2624062074351, (5, 2433): 813.360545744168, (5, 2436): 812.8846804821758, (5, 2437): 806.8501601133739, (5, 2440): 808.170355642098, (5, 2445): 835.062242187181, (5, 2447): 831.7659576515309, (5, 2454): 834.8456773617469, (5, 2455): 834.9971336743289, (5, 2460): 825.4598258509355, (5, 2461): 826.641374644979, (5, 2471): 845.8176094900751, (5, 2492): 826.0278307903644, (5, 2511): 816.4390187171404, (5, 2523): 821.3459957997311, (5, 2525): 819.9167761608354, (5, 2535): 822.2565737228394, (5, 2537): 820.1514181322942, (5, 2538): 821.5962909263538, (5, 2539): 821.0146695884611, (5, 2540): 823.2125459792147, (5, 2542): 824.7493871924457, (5, 2559): 854.6691483090831, (5, 2575): 852.001456630538, (5, 2599): 806.4455738498829, (5, 2600): 816.6549683733966, (5, 2607): 810.7128217075091, (5, 2627): 822.3379743722898, (5, 2647): 827.9111003295899, (5, 2674): 825.0549610369652, (5, 2681): 824.2744671475317, (5, 2683): 827.0005460329088, (5, 2686): 823.875030450391, (5, 2689): 860.2037180176902, (5, 2690): 860.3784244089129, (5, 2713): 867.3257748657265, (5, 2714): 867.9233178043283, (5, 2715): 868.8175519602643, (5, 2739): 868.0283877638398, (5, 2740): 862.4195938906558, (5, 2741): 862.8663637612575, (5, 2749): 866.7788551816549, (5, 2750): 867.0634657276759, (5, 2752): 867.7034066088547, (5, 2755): 868.4075326123998, (5, 2758): 868.1969295699034, (5, 2759): 868.2022574011594, (5, 2769): 867.1688918043764, (5, 2771): 863.8561173254667, (5, 2779): 864.1052230800041, (5, 2784): 854.0186993725772, (5, 2800): 855.7824106815176, (5, 2802): 860.6743540384845, (5, 2803): 860.3369706496524, (5, 2804): 859.7402100190772, (5, 2805): 861.4184149394217, (5, 2807): 861.3658778963045, (5, 2809): 861.0252494600138, (5, 2812): 855.2907032016349, (5, 2814): 860.697406672326, (5, 2817): 860.8520404791731, (5, 2819): 861.4902089072983, (5, 2823): 855.8171756717475, (5, 2832): 862.5254625361138, (5, 2836): 858.4954616472695, (5, 2839): 861.3562210172653, (5, 2841): 861.0738460895151, (5, 2843): 860.781965685892, (5, 2846): 859.2755769990445, (5, 2849): 863.1480061488779, (5, 2852): 862.2352384399213, (5, 2853): 863.5678790405349, (5, 2876): 863.9560034865232, (5, 2877): 867.1854466203908, (5, 2885): 868.1137511454558, (5, 2918): 861.9618524948685, (5, 2921): 863.3510722446132, (5, 2925): 856.8278518802138, (5, 2926): 854.6437438539255, (5, 2930): 859.5586760490238, (5, 2931): 857.429281764622, (5, 2938): 861.9769045638202, (5, 2940): 866.0259792380442, (5, 2947): 861.2731277948436, (5, 2949): 859.5231321891833, (5, 2950): 860.1466535673892, (5, 2952): 859.4597376924912, (5, 2958): 859.3266939768185, (5, 2959): 859.9908081239879, (5, 2960): 861.5202070937945, (5, 2961): 860.7848295352859, (5, 2963): 858.7436252967008, (5, 2968): 859.1793866513322, (5, 2976): 858.5621031296088, (5, 2981): 845.4770269763319, (5, 2982): 845.0961725486331, (5, 2984): 844.4156863747584, (5, 3003): 843.2167935039934, (5, 3046): 834.3375685334266, (5, 3050): 841.3305040386994, (5, 3051): 841.8684034402858, (5, 3053): 840.368438439212, (5, 3069): 848.7463467985783, (5, 3071): 840.0075226276581, (5, 3080): 868.115811063094, (5, 3199): 840.9651585641584, (5, 3200): 839.3782288766215, (5, 3205): 849.1375025607267, (5, 3209): 840.2045923617319, (5, 3215): 839.4788493652458, (5, 3217): 837.5294536195213, (5, 3249): 839.658804738724, (5, 3263): 854.3783765613605, (5, 3289): 844.3135760099309, (5, 3301): 844.7772029872323, (5, 3302): 844.0765575106461, (5, 3307): 843.2018439889621, (5, 3310): 845.6162999630063, (5, 3391): 847.1288137016169, (5, 3509): 530.4319245839607, (5, 3510): 529.03920543654, (5, 3511): 529.9643894165694, (5, 3512): 529.1006316224177, (5, 3514): 529.3912335259423, (5, 3519): 533.7086346098583, (5, 3536): 532.8846007194875, (5, 3545): 535.067338810107, (5, 3548): 532.9278598799727, (5, 3572): 533.6785641934816, (5, 3581): 531.9987504920969, (5, 3583): 531.0411014096862, (5, 3601): 536.3270642774543, (5, 3656): 534.0726019346704, (5, 3669): 531.3593070371721, (5, 3670): 532.6087068626276, (5, 3695): 525.4685865448683, (5, 3696): 526.455302862614, (5, 3782): 533.3544836692639, (5, 3792): 531.8389246392497, (5, 3989): 90.02766223452214, (5, 4008): 97.33225941328757, (5, 4031): 99.94902364742178, (5, 4045): 94.40057001569134, (5, 4144): 91.98378553463247, (5, 4145): 81.56736673840285, (5, 4164): 88.41751119683224, (5, 4168): 84.71425091185019, (5, 4173): 83.55678067266398, (5, 4181): 79.03650292152824, (5, 4228): 78.12732535489053, (5, 4248): 71.81712486176906, (5, 4254): 24.0, (5, 4260): 24.0, (5, 4262): 24.0, (5, 4273): 24.0, (5, 4319): 24.0, (5, 4326): 24.0, (5, 4328): 24.0, (5, 4334): 24.0, (5, 4335): 24.0, (5, 4372): 245.50052283370988, (5, 4413): 260.7755489156028, (5, 4434): 243.47240660845645, (5, 4447): 239.45326419266726, (5, 4452): 244.39511568295927, (5, 4463): 264.7590447339959, (5, 4465): 263.04026523493116, (5, 4619): 277.9186999580564, (5, 4645): 276.2224733022677, (5, 4657): 278.09654304186154, (5, 4666): 279.57778506263844, (5, 4676): 280.0829789740987, (5, 4678): 279.256208397967, (5, 4689): 281.27016112298276, (5, 4704): 284.6568025878277, (5, 4726): 337.5733568137916, (5, 4727): 336.7536405454677, (5, 4730): 335.03903454969424, (5, 4731): 336.36824932950753, (5, 4734): 332.47309736050164, (5, 4735): 332.4180618380274, (5, 4736): 333.4363769710653, (5, 4737): 332.9127868367209, (5, 4738): 333.6027992534409, (5, 4756): 334.80519433793904, (5, 4760): 327.17261168115357, (5, 4761): 326.2123259655505, (5, 4762): 326.92237166102774, (5, 4765): 327.9989803635169, (5, 4773): 338.49121115931945, (5, 4774): 338.90929745798746, (5, 4790): 337.77339223448985, (5, 4795): 336.7686381420892, (5, 4799): 339.8723582446016, (5, 4801): 343.159549643641, (5, 4804): 335.6067823336811, (5, 4805): 334.7976101584329, (5, 4806): 340.2932099146123, (5, 4815): 340.52089373193314, (5, 4816): 342.0470863196424, (5, 4817): 343.7728283198573, (5, 4826): 342.14663494638523, (5, 4830): 341.5504890794795, (5, 4839): 329.6148382647272, (5, 4840): 330.9162298542916, (5, 4841): 329.66263132463945, (5, 4846): 328.8722316003775, (5, 4848): 329.84154649183483, (5, 4850): 330.7773032360191, (5, 4871): 316.0785746206558, (5, 4883): 324.572365384766, (5, 4900): 318.5641069232281, (5, 4901): 318.4855729114318, (5, 4917): 301.0550312928142, (5, 4931): 297.4531567486039, (5, 4944): 300.59058503694814, (5, 4956): 298.98506103322353, (5, 4958): 300.61966519113736, (5, 4959): 301.1363209537602, (5, 4961): 298.99951442466687, (5, 4966): 299.12443869392524, (5, 5207): 295.44917151088754, (5, 5272): 196.30768654368867, (5, 5283): 197.01483348615832, (5, 5287): 202.36513500475965, (5, 5289): 202.8718170959728, (5, 5293): 192.4035897790368, (5, 5295): 193.8367481549406, (5, 5296): 196.36253135872826, (5, 5298): 197.75890780953722, (5, 5303): 200.41981444809116, (5, 5305): 200.8987545507525, (5, 5306): 204.07379634750723, (5, 5307): 200.85749466524078, (5, 5308): 201.95262851914626, (5, 5313): 198.75637816672008, (5, 5314): 198.1269135001269, (5, 5317): 203.60027138887244, (5, 5319): 200.4630968973118, (5, 5324): 198.2028808724695, (5, 5326): 196.61064542794028, (5, 5348): 206.12025010647184, (5, 5351): 210.021745257468, (5, 5399): 206.93747129146266, (5, 5413): 216.32079094328796, (5, 5422): 204.7399537282738, (5, 5445): 204.53339475164313, (5, 5448): 204.06417287320818, (5, 5456): 206.63394341498056, (5, 5467): 207.78632030208817, (5, 5624): 195.91812472660465, (5, 5671): 179.05914751593437, (5, 5672): 177.40001722903384, (5, 5797): 200.327545128379, (5, 5871): 241.54829477640058, (5, 5976): 233.57205599208731, (5, 6118): 699.150067576338, (5, 6248): 729.1845131030009, (5, 6345): 221.107071193444, (5, 6352): 228.03079620910498, (5, 6354): 219.27810979096665, (5, 6359): 218.15816533418987, (5, 6376): 227.58604000258768, (5, 6378): 220.12559131960478, (5, 6381): 218.90004447682625, (5, 6383): 222.4748468747547, (5, 6396): 220.76403920938768, (5, 6399): 221.3268880441477, (5, 6408): 227.52520748798239, (5, 6409): 223.64590945945588, (5, 6419): 233.83498318054097, (5, 6422): 226.1135961267747, (5, 6423): 226.63553491354517, (5, 6424): 219.2611172983494, (5, 6439): 220.391433792164, (5, 6464): 222.11397020308127, (5, 6465): 222.99909103164347, (5, 6469): 222.58155347806553, (5, 6470): 223.10975911984733, (5, 6472): 215.91094168034215, (5, 6480): 216.30521303441552, (5, 6486): 211.29466307116132, (5, 6497): 212.9049432034168, (5, 6503): 220.59307890924995, (5, 6508): 220.66519813416298, (5, 6509): 219.08587076743086, (5, 6521): 215.02259083508014, (5, 6544): 214.93818071288413, (5, 6552): 223.8904195571113, (5, 6553): 224.89342763886074, (5, 6554): 225.92159958339843, (5, 6578): 222.29884511647208, (5, 6582): 222.47503694684613, (5, 6601): 221.70988519205505, (5, 6609): 214.16917647807585, (5, 6610): 213.73486221351524, (5, 6611): 213.9067020642354, (5, 6614): 214.67497898622955, (5, 6615): 214.34831073651372, (5, 6616): 212.7858098645967, (5, 6617): 213.4251669664609, (5, 6618): 211.43368073041643, (5, 6619): 215.34301227631963, (5, 6620): 212.54074417444164, (5, 6621): 213.372239653172, (5, 6622): 213.3196935928906, (5, 6623): 214.50455889700936, (5, 6624): 215.039875548366, (5, 6625): 215.32981116051667, (5, 6626): 215.49924758261545, (5, 6627): 215.1089124685322, (5, 6628): 212.50323433141884, (5, 6629): 214.5190510538953, (5, 6630): 216.46952530027082, (5, 6632): 214.7328692799305, (5, 6634): 217.26112458808606, (5, 6635): 213.8059823763973, (5, 6636): 212.65842943474567, (5, 6637): 215.69859796782185, (5, 6638): 216.13116109236537, (5, 6639): 214.87189121018568, (5, 6640): 216.10554435132335, (5, 6641): 213.22672232302818, (5, 6642): 215.95303599879884, (5, 6643): 215.77659034295573, (5, 6645): 215.11011695883653, (5, 6646): 211.92159544605352, (5, 6647): 215.7758210782243, (5, 6653): 214.46300063853624, (5, 6655): 214.94300383641374, (5, 6658): 217.23242020717097, (5, 6662): 215.83791707701843, (5, 6819): 263.47023597354854, (5, 6996): 245.14072272340775, (5, 7059): 233.55229809212418, (5, 7187): 255.92470825704154, (5, 7304): 277.983439789958, (5, 7528): 246.26996375792606, (5, 7720): 177.3949338163899, (5, 7793): 179.02521100551687, (5, 7807): 177.981165154189, (5, 7808): 179.4605115981121, (5, 7831): 206.36527556778515, (5, 7850): 196.28450726401806, (5, 7852): 199.14872430176214, (5, 8012): 180.89789880350386, (5, 8125): 176.89293696038996, (5, 8208): 156.30021726068563, (5, 8392): 196.0748150019277, (5, 8651): 319.2023319311874, (5, 9088): 271.3879543750509, (5, 9443): 345.73756056709647, (5, 9444): 344.2047409810156, (5, 9828): 399.1670108213071, (5, 9868): 397.68758661417377, (5, 10180): 176.84934570371524, (5, 10256): 151.43742234420736, (5, 10276): 160.87101016243457, (5, 10378): 152.27880030633733, (5, 10676): 196.93989223587639, (5, 10714): 216.97386691576511, (5, 10730): 205.245111563987, (5, 10862): 354.73553461282813, (5, 10881): 353.69436079891193, (5, 10883): 354.50963692616523, (5, 10885): 354.78985816938336, (5, 10891): 355.793964589405, (5, 10909): 354.21361650116893, (5, 10911): 352.3526062546593, (5, 10913): 353.1466818582912, (5, 10915): 352.273904902535, (5, 10919): 351.3857587070706, (5, 11037): 379.8164856046732, (5, 11039): 375.8299086713075, (5, 11516): 195.9584617811901, (5, 11856): 24.0, (5, 11857): 24.0, (5, 11861): 24.0, (5, 11881): 24.0, (5, 11902): 24.0, (5, 11911): 24.0, (5, 11914): 24.0, (5, 11922): 24.0, (5, 11924): 24.0, (5, 11926): 24.0, (5, 11950): 24.0, (5, 11963): 24.0, (5, 11983): 24.0, (5, 11985): 24.0, (5, 12009): 24.0, (5, 12010): 24.0, (5, 12018): 24.0, (5, 12020): 24.0, (5, 12021): 24.0, (5, 12024): 24.0, (5, 12025): 24.0, (5, 12027): 24.0, (5, 12031): 24.0, (5, 12032): 24.0, (5, 12035): 24.0, (5, 12041): 24.0, (5, 12045): 42.395351292958196, (5, 12145): 24.0, (5, 12275): 99.79496729226489, (5, 12294): 99.253796498563, (5, 12358): 119.65396222612515, (5, 12463): 130.7778210338647, (5, 12465): 130.80093131232053, (5, 12482): 130.54875077523238, (5, 12503): 130.93899592632675, (5, 12506): 131.73174796609177, (5, 12549): 126.06453583787886, (5, 12559): 126.23214653559155, (5, 12569): 128.28777203860648, (5, 12572): 128.80633367445884, (5, 12574): 127.28821792128576, (5, 12576): 126.30594431091778, (5, 12591): 123.97209592693113, (5, 12608): 127.6250735995288, (5, 12696): 117.9517046958046, (5, 12710): 120.11024493522473, (5, 12728): 120.58961624834954, (5, 12766): 140.35352656371782, (5, 12771): 140.51133895882305, (5, 12790): 141.76343785208473, (5, 12795): 145.4610121155346, (5, 12797): 151.51408714767038, (5, 12798): 149.91794939241169, (5, 12811): 142.40657229653584, (5, 12830): 146.04436634072098, (5, 12848): 142.42671338371116, (5, 12850): 140.43248361713097, (5, 12852): 145.70273846659936, (5, 12854): 146.87119380567293, (5, 12859): 140.65927004430947, (5, 12861): 148.10970943467368, (5, 12865): 142.05281160536404, (5, 12866): 141.93142765502324, (5, 12867): 140.29404653145144, (5, 12874): 141.18065946867978, (5, 12875): 140.01354381707642, (5, 12881): 144.37043467183508, (5, 12883): 142.87402445199308, (5, 12885): 139.43370577013795, (5, 12888): 143.06411546148638, (5, 12889): 142.93023879100068, (5, 12892): 141.21308004829035, (5, 12893): 143.49635100354192, (5, 12896): 142.3198187377682, (5, 12906): 143.32631092262773, (5, 13018): 167.01267052902412, (5, 13071): 170.13005176962267, (5, 13131): 167.40520743560498, (5, 13146): 157.23245637143953, (5, 13159): 182.7664723907779, (5, 13193): 168.19417270556167, (5, 13198): 178.89302862982197, (5, 13292): 160.71737674286592, (5, 13296): 151.82250147857522, (5, 13406): 194.4023648090822, (5, 13407): 195.40345114140487, (5, 13417): 200.7567918986059, (5, 13418): 199.91795520179724, (5, 13438): 190.08901844779862, (5, 13442): 187.3670389714365, (5, 13443): 188.78983844240082, (5, 13764): 329.3814160347501, (5, 13766): 327.6367231344698, (5, 13771): 330.815372394892, (5, 13783): 328.4321912403736, (5, 13784): 325.1006181427537, (5, 13792): 336.4198980798404, (5, 13824): 329.9199349998969, (5, 14017): 311.5987631975467, (5, 14870): 319.4719393195852, (5, 14997): 264.7862814998273, (5, 15000): 264.7087955307848, (5, 15003): 263.6097429873353, (5, 15006): 260.4629326835387, (5, 15007): 259.2410447719202, (5, 15056): 259.6814881163266, (5, 15063): 260.84132583887714, (5, 15069): 261.387025986314, (5, 15076): 259.1047649610661, (5, 15086): 262.8676098482564, (5, 15087): 264.2992286157858, (5, 15111): 267.91890068950715, (5, 15116): 265.8457698023429, (5, 15722): 298.4559980134323, (5, 15998): 324.15299219509717, (5, 16073): 592.5354711145777, (5, 16939): 742.0409364955391, (5, 16940): 740.2245165921005, (5, 16951): 742.3368948149806, (5, 16963): 742.5006391857543, (5, 16965): 744.6914974006679, (5, 16969): 744.1826607514562, (5, 16970): 743.2851252950438, (5, 16971): 741.3094977372139, (5, 16973): 741.1930604862121, (5, 16974): 745.5876843884212, (5, 16976): 743.427872372802, (5, 16978): 741.978761586634, (5, 16980): 744.1438031451296, (5, 16982): 745.5890057636371, (5, 17045): 806.8799504210308, (5, 17048): 809.4390899217782, (5, 17304): 57.56520993269629, (5, 17305): 58.647071364180164, (5, 17330): 58.951104554182976, (5, 17334): 55.13415075663925, (5, 17343): 60.90249952432722, (5, 17345): 57.319302491147795, (5, 17347): 60.292223543102274, (5, 17351): 52.384771864156406, (5, 17372): 55.74873732792913, (5, 17373): 60.44656168025871, (5, 17377): 60.95691853019918, (5, 17382): 58.371939782298064, (5, 17383): 58.10339983892796, (5, 17389): 56.75915580098668, (5, 17400): 59.03558001018141, (5, 17401): 58.64030667578707, (5, 17402): 59.39985119624069, (5, 17403): 59.836706507126905, (5, 17440): 60.043128439043755, (5, 17455): 61.93533670958258, (5, 17491): 63.89309832840157, (5, 17507): 48.804434213402324, (5, 17509): 49.7932517631516, (5, 17590): 54.158108338207164, (5, 17615): 33.055086961526776, (5, 17642): 35.35322098164489, (5, 17643): 35.868436698480174, (5, 17668): 32.63553453275083, (5, 17721): 26.587392016348755, (5, 17754): 41.34051900543705, (5, 17769): 47.27896278981064, (5, 17776): 45.07573536899978, (5, 17804): 49.42125369269981, (5, 17809): 50.92551505453628, (5, 17824): 49.01376439517854, (5, 17837): 49.97456270149518, (5, 17838): 51.318089838386115, (5, 17862): 50.90998713446617, (5, 17866): 53.210531837243686, (5, 17872): 49.19198532286967, (5, 17873): 47.811581862251906, (5, 17881): 50.15634765902949, (5, 17947): 592.0229569363094, (5, 17951): 588.6847848439223, (5, 17953): 587.9818423452697, (5, 17954): 588.1727267835702, (5, 17959): 591.4489007792198, (5, 17963): 590.3852036353757, (5, 18000): 573.2189229832655, (5, 18001): 573.8019048446746, (5, 18111): 618.8280552878317, (5, 18148): 532.2191341673386, (5, 18166): 565.4158571942083, (5, 18189): 597.0323875607725, (5, 18239): 60.32056058756683, (5, 18240): 60.53688814817612, (5, 18245): 60.568922587351786, (5, 18247): 60.51826725907732, (5, 18251): 60.847620103647714, (5, 18256): 61.47799968340233, (5, 18258): 61.272729675074885, (5, 18259): 61.46204165924721, (5, 18260): 61.773596150176274, (5, 18262): 62.19059302135829, (5, 18263): 61.70190323238359, (5, 18264): 61.99570150066344, (5, 18266): 62.50430632107796, (5, 18267): 62.75952739254589, (5, 18268): 62.97491748272577, (5, 18269): 63.509976675508895, (5, 18275): 63.25856170436123, (5, 18285): 61.80268816178272, (5, 18308): 56.26600966429106, (5, 18313): 55.03606199809574, (5, 18314): 56.30673493093542, (5, 18315): 62.819816806149404, (5, 18316): 63.10315402500434, (5, 18317): 63.37324640882231, (5, 18320): 63.16369956553143, (5, 18321): 63.45599682396771, (5, 18322): 63.816053622452316, (5, 18324): 63.65402314585071, (5, 18325): 64.33118740016317, (5, 18326): 64.06422170819056, (5, 18327): 63.89104643155911, (5, 18329): 64.28540920814251, (5, 18330): 64.93165061027922, (5, 18331): 64.32249523892445, (5, 18332): 63.86095263304601, (5, 18333): 64.57680462979152, (5, 18336): 63.72238267712611, (5, 18337): 63.75184240941856, (5, 18403): 65.21567150215044, (5, 18432): 67.33544742632748, (5, 18451): 65.59708423596673, (5, 18466): 64.54187452922338, (5, 18481): 62.16215107355961, (5, 18483): 62.382779835879795, (5, 18484): 61.8389311093386, (5, 18485): 59.97893979430083, (5, 18486): 60.21919987862336, (5, 18487): 59.08057923300209, (5, 18489): 60.8440119495216, (5, 18490): 61.1360507632724, (5, 18491): 61.55018376449602, (5, 18492): 58.376458839949024, (5, 18493): 59.81831672906096, (5, 18494): 60.853873421249816, (5, 18495): 60.79566018954332, (5, 18496): 60.53803232502067, (5, 18497): 58.62190824030314, (5, 18498): 59.696916839611745, (5, 18499): 60.42070492305504, (5, 18501): 59.51533324887553, (5, 18502): 59.02696368087569, (5, 18503): 58.91526847366287, (5, 18504): 60.975143346296, (5, 18506): 58.9733696609377, (5, 18507): 58.38759108612394, (5, 18508): 60.11013705694678, (5, 18509): 59.91553715989787, (5, 18510): 58.62531383081876, (5, 18511): 59.52837199229338, (5, 18512): 59.382068346318945, (5, 18515): 60.71235480065416, (5, 18516): 60.049849041559376, (5, 18517): 59.132794159491866, (5, 18518): 60.61612049338326, (5, 18519): 61.19981113269926, (5, 18520): 60.23259099222166, (5, 18522): 63.56103035028942, (5, 18523): 63.4176755094569, (5, 18532): 63.69508844586723, (5, 18535): 62.87901292213254, (5, 18537): 62.43028846851656, (5, 18539): 62.39814591523068, (5, 18540): 62.31822060873435, (5, 18541): 62.43230128693617, (5, 18542): 62.528483477620846, (5, 18543): 61.95979022410549, (5, 18546): 61.82532691117864, (5, 18555): 62.5238073214463, (5, 18556): 62.49516408033463, (5, 18565): 63.32715165555245, (5, 18567): 63.08128803219937, (5, 18568): 62.88838493526162, (5, 18577): 65.81068524111205, (5, 18583): 65.92052636852534, (5, 18605): 67.27762708051101, (5, 18608): 62.43441932316579, (5, 18616): 70.00352866306423, (5, 18618): 72.05750996295984, (5, 18625): 72.7446951095991, (5, 18645): 71.35628000146005, (5, 18646): 71.3421672109691, (5, 18653): 67.85178988934746, (5, 18654): 69.68918925484351, (5, 18655): 68.15012637688373, (5, 18666): 78.56780182987755, (5, 18837): 101.0072993549007, (5, 18974): 72.29153415730524, (5, 18999): 77.39529669461562, (5, 19000): 77.97216743141018, (5, 19174): 88.6402731835439, (5, 19342): 98.15199309640603, (5, 19455): 70.31154690650585, (5, 19555): 93.41734360194718, (5, 19564): 102.02612461161414, (5, 19573): 100.72134960179373, (5, 19586): 99.53122728216827, (5, 19605): 97.64475504535629, (5, 19611): 98.11098987158411, (5, 19614): 95.22571372191831, (5, 19641): 93.89683713595404, (5, 19702): 97.2007287450667, (5, 19713): 96.38771862205242, (5, 19731): 83.98653778655755, (5, 19819): 77.05639968046414, (5, 19893): 103.80243679140484, (5, 19899): 108.63111171897076, (5, 19929): 102.6227762664745, (5, 19951): 105.96850102746333, (5, 19962): 106.99940979023269, (5, 19970): 98.4289201450499, (5, 19971): 100.50164080860492, (5, 19972): 101.87814986646768, (5, 19975): 100.39739316599487, (5, 19978): 97.37222376576813, (5, 19987): 95.99980277549709, (5, 19989): 94.4788161901156, (5, 20039): 95.60615574255642, (5, 20043): 94.33740818115041, (5, 20047): 91.91593490185913, (5, 20052): 91.85560102526834, (5, 20054): 92.92641888054898, (5, 20085): 91.03894594354905, (5, 20104): 91.65335068154383, (5, 20132): 90.6173749765799, (5, 20203): 122.36313362108407, (5, 20280): 128.37877043909938, (5, 20285): 130.91104751888707, (5, 20290): 127.20339279784625, (5, 20297): 126.75283515014756, (5, 20309): 113.44659271333849, (5, 20453): 111.85704202826996, (5, 20485): 125.65591431865096, (5, 20520): 125.30560778306395, (5, 20526): 131.36908765328678, (5, 20698): 403.46302073083643, (5, 20868): 466.59401976504637, (5, 21042): 123.83890864285247, (5, 21057): 111.07460745461441, (5, 21066): 117.10332094775256, (5, 21075): 119.82677922113508, (5, 21093): 122.65303838256452, (5, 21098): 113.3073578561883, (5, 21127): 122.64839230287498, (5, 21130): 120.11824758765842, (5, 21144): 120.70475275405761, (5, 21146): 123.49192905036891, (5, 21147): 121.00860254131447, (5, 21148): 118.67945829507163, (5, 21153): 125.86632090307826, (5, 21293): 102.21420017940942, (5, 21426): 114.18075805158955, (5, 21442): 106.09274616003029, (5, 21451): 105.33373500794285, (5, 21466): 109.048652602329, (5, 21469): 107.0281750467896, (5, 21471): 110.10880578870304, (5, 21473): 108.24295928352073, (5, 21475): 109.69859685428533, (5, 21482): 106.42089101586902, (5, 21484): 106.48628199679938, (5, 21488): 107.84869424372268, (5, 21494): 108.83757129637087, (5, 21498): 107.54381011717162, (5, 21500): 108.93440743701191, (5, 21514): 102.2723311681169, (5, 21537): 107.58870584037511, (5, 21662): 98.76483690770563, (5, 21691): 106.40444807484697, (5, 21757): 124.89729595573547, (5, 21777): 149.04882519455964, (5, 21778): 151.08159851743014, (5, 21779): 150.09359049775463, (5, 21790): 146.62805267223365, (5, 21802): 146.99697744192332, (5, 21824): 145.05818601202088, (5, 21874): 149.7832363105457, (5, 21879): 151.37320508801056, (5, 21983): 141.69961313993966, (5, 22002): 120.25024494692312, (5, 22132): 137.86244840180314, (5, 22261): 419.25122205568545, (5, 22298): 415.3595433234174, (5, 22339): 440.30588402553764, (5, 22508): 378.80994042659955, (5, 22841): 836.3192020995848, (5, 22842): 836.4055837727109, (5, 22874): 831.7169277209392, (5, 22941): 831.9653952523603, (5, 22956): 835.053955335684, (5, 22960): 835.7623067358016, (5, 22968): 839.7548398143367, (5, 22970): 840.4433460372933, (5, 22974): 842.5377029114197, (5, 22980): 846.1757868386914, (5, 23025): 846.6229103055982, (5, 23028): 845.9713191975372, (5, 23081): 853.0063843316142, (5, 23104): 847.5826660181668, (5, 23147): 813.4574441427891, (5, 23298): 66.0246420084414, (5, 23376): 71.0180211752525, (5, 23381): 71.51796966605306, (5, 23529): 60.05140846486152, (5, 23556): 63.42981981895848, (5, 23718): 72.27090854653926, (5, 24001): 43.25189742707091, (5, 24094): 25.72556781980446, (5, 24129): 24.0, (5, 24174): 25.223151940412592, (5, 24235): 24.0, (5, 24259): 24.0, (5, 24260): 24.0, (5, 24261): 24.0, (5, 24305): 24.0, (5, 24306): 24.0, (5, 24307): 24.0, (5, 24308): 48.833002211429566, (5, 24498): 38.502076971709705, (5, 24499): 38.31897610077345, (5, 24500): 37.95858986291575, (5, 24668): 49.42353037614243, (5, 24711): 37.98617277104353, (5, 24756): 37.47685225678486, (5, 24788): 40.326442604224276, (5, 24809): 31.413129105802213, (5, 24813): 34.47292156818352, (5, 24821): 33.594494634476796, (5, 24825): 33.695205545425345, (5, 24832): 31.24765905787644, (5, 24833): 32.28949887467524, (5, 24835): 33.16579838646227, (5, 24837): 35.21216439779033, (5, 24840): 30.885285763751362, (5, 24841): 32.91113366798395, (5, 24844): 30.66432654053829, (5, 24845): 32.680562955584406, (5, 24846): 31.113192489619117, (5, 24849): 31.564814212916005, (5, 24850): 34.45784983256125, (5, 24863): 24.0, (5, 24866): 24.578603509276455, (5, 24885): 25.507805899071, (5, 24886): 24.964534779006907, (5, 24889): 31.383226086027786, (5, 24903): 34.0082437156765, (5, 24909): 29.665218506163132, (5, 24999): 115.71264662970503, (5, 25019): 115.73053645033966, (5, 25028): 114.1228176986962, (5, 25137): 153.61244353119082, (5, 25145): 152.5766902979202, (5, 25208): 167.3707857661835, (5, 25233): 168.9294297301012, (5, 25371): 138.26832321877325, (5, 25377): 136.85419170004042, (5, 25828): 209.34711455203305, (5, 25851): 218.188723550807, (5, 25874): 205.9657800062656, (5, 25898): 205.86584361714552, (5, 25946): 210.42315546680229, (5, 26047): 195.9363232754568, (5, 26066): 132.42592859285713, (5, 26197): 167.84533723743905, (5, 26212): 274.7847772822735, (5, 26253): 281.3406794624877, (5, 26254): 278.4572597788569, (5, 26257): 277.4042904884728, (5, 26258): 280.38206807261196, (5, 26260): 278.7574509167465, (5, 26266): 278.4716674919042, (5, 26267): 276.96691637929894, (5, 26271): 277.2419056226666, (5, 26304): 252.95778343573673, (5, 26305): 252.2837716706178, (5, 26363): 221.26164044729487, (5, 26441): 427.85949749875573, (5, 26442): 427.2768935488713, (5, 26450): 423.9825946663572, (5, 26459): 423.3534266882533, (5, 26462): 423.6508330188246, (5, 26467): 433.25361846833204, (5, 26471): 430.74714413119597, (5, 26472): 430.5164630994166, (5, 26473): 430.4586868590889, (5, 26476): 429.47209093432184, (5, 26485): 425.1678107426619, (5, 26493): 425.4597078060808, (5, 26524): 424.92807476650125, (5, 26525): 424.6513952759122, (5, 26556): 429.4308465303641, (5, 26560): 428.80756363679353, (5, 26561): 426.6609008427759, (5, 26564): 428.62894522676555, (5, 26569): 426.2563057001718, (5, 26570): 425.5473116601148, (5, 26573): 426.2432116715244, (5, 26581): 426.3204342460848, (5, 26583): 425.5084579095244, (5, 26593): 426.53838693478156, (5, 26837): 434.05873663311246, (5, 26844): 436.1810625373942, (5, 26863): 431.93727695618605, (5, 26893): 438.19564007238876, (5, 26902): 441.0898334514845, (5, 26905): 437.82524104623775, (5, 26912): 440.19111567315554, (5, 26921): 434.91167714908204, (5, 26922): 429.66360738592414, (5, 27212): 441.71408576992036, (5, 27218): 438.7910277512613, (5, 27239): 445.9760390727472, (5, 27257): 443.8897866699795, (5, 27274): 446.8850483187211, (5, 27279): 446.52541737567293, (5, 27282): 444.0457425928017, (5, 27283): 444.8148267462974, (5, 27285): 448.0725569432899, (5, 27286): 445.9889893645762, (5, 27290): 441.9440687768038, (5, 27295): 440.2541703596791, (5, 27300): 447.2702705883158, (5, 27344): 441.1232894766694, (5, 27366): 444.03630057775825, (5, 27383): 448.5152222656477, (5, 27398): 451.2775594853022, (5, 27406): 448.7327253431994, (5, 27407): 449.37936721015046, (5, 27426): 445.4043801686009, (5, 27432): 434.8919675640946, (5, 27460): 441.377600804085, (5, 27523): 446.6123118537549, (5, 27545): 488.6239030437455, (5, 27602): 545.8420643983573, (5, 27606): 546.751083238195, (5, 27646): 489.6983334314002, (5, 27667): 501.0617713980489, (5, 27672): 501.573685058123, (5, 27674): 499.68869444559834, (5, 27688): 500.9807199990267, (5, 27692): 503.6353168825851, (5, 27693): 501.9517299372555, (5, 27705): 501.95804255215893, (5, 27712): 502.8665560203504, (5, 27786): 544.9528151145267, (5, 27790): 537.288391998255, (5, 27791): 536.5660806846364, (5, 27795): 541.8632546566025, (5, 27801): 536.2687393841519, (5, 27813): 546.8500376826327, (5, 27816): 544.5253886229114, (5, 27823): 536.0452862359399, (5, 27830): 541.7220218706685, (5, 27884): 471.76121226166543, (5, 27885): 485.07956963616556, (5, 27896): 476.972498337685, (5, 27919): 476.321193534958, (5, 27922): 478.1202709877243, (5, 27930): 473.66046501435164, (5, 27934): 474.25608207633877, (5, 27935): 474.7306445211118, (5, 27948): 544.2506727924083, (5, 27951): 546.0163462581207, (5, 28061): 500.23149141525096, (5, 28290): 616.3019799291823, (5, 28292): 618.8245075848412, (5, 28293): 616.8031384606206, (5, 28295): 615.8674662861049, (5, 28296): 616.2205711282129, (5, 28297): 614.9686153152086, (5, 28302): 614.1863737869569, (5, 28310): 656.2002479032756, (5, 28313): 657.8688453659121, (5, 28372): 658.535299769575, (5, 28398): 658.7025636380175, (5, 28399): 657.899948618696, (5, 28400): 659.1591624210771, (5, 28401): 655.8950069534391, (5, 28445): 656.6004823407828, (5, 28475): 653.5830533336084, (5, 28885): 24.0, (5, 28886): 24.0, (5, 28915): 24.0, (5, 28916): 24.0, (5, 28917): 24.0, (5, 28921): 24.0, (5, 28931): 24.0, (5, 28945): 30.47816233321342, (5, 28982): 25.60828082071036, (5, 29219): 44.81102297363434, (5, 29228): 45.04139027646394, (5, 29246): 62.81818511707735, (5, 29248): 66.62975069798371, (5, 29282): 62.63286415917557, (5, 29290): 60.559364585931895, (5, 29291): 60.877584258699144, (5, 29292): 61.13376479344085, (5, 29293): 59.524348705560335, (5, 29294): 62.45142086754103, (5, 29298): 60.68177904588587, (5, 29299): 61.607496649795955, (5, 29304): 57.83877036815632, (5, 29317): 53.070734442157026, (5, 29323): 52.596995325819144, (5, 29330): 55.00765254419282, (5, 29331): 55.34593957949608, (5, 29344): 53.30555441239295, (5, 29445): 88.55818975082774, (5, 29724): 823.4851213711826, (5, 29738): 824.4637620311123, (5, 29745): 821.4286460418207, (5, 29748): 821.0736636037562, (5, 29750): 822.2836231188379, (5, 29759): 819.8450268907158, (5, 29772): 823.4475727952741, (5, 29781): 822.6345552768164, (5, 29784): 822.4125250042438, (5, 29790): 823.2563958858518, (5, 29811): 820.7948213611658, (5, 29817): 825.0063915136053, (5, 29818): 824.1976423429331, (5, 29929): 821.6543046693915, (5, 30039): 836.8632415877852, (5, 30066): 830.0044188892867, (5, 30116): 794.8821402259796, (5, 30238): 742.8697912988868, (5, 30248): 770.9787936490999, (5, 30260): 771.7733226789564, (5, 30545): 25.686938268580604, (5, 30733): 78.76938548000216, (5, 30756): 92.95253378098658, (5, 30921): 66.81633074165292, (5, 31079): 230.21188193950647, (5, 31149): 226.77991230509414, (5, 31154): 228.06181689673716, (5, 31160): 226.91892352487793, (5, 31163): 228.69807581957522, (5, 31189): 243.34202182252963, (5, 31215): 243.5524049957705, (5, 31259): 251.4211966808718, (5, 31262): 252.6551397605382, (5, 31430): 233.64034010628126, (5, 31568): 288.31950401686464, (5, 31751): 241.91375965141918, (6, 109): 121.44006232706623, (6, 872): 437.06070262105425, (6, 873): 439.57146212612633, (6, 877): 439.21347493611495, (6, 879): 439.64271388991693, (6, 884): 438.43264692823107, (6, 889): 439.72544570294144, (6, 891): 437.4458540842168, (6, 892): 441.4681215617443, (6, 894): 440.9121733709529, (6, 896): 437.5236533985545, (6, 903): 439.9755445716845, (6, 909): 433.7849149630816, (6, 910): 434.2478589078402, (6, 912): 432.7158638558714, (6, 913): 431.2286860216744, (6, 916): 429.80599717958177, (6, 926): 434.360301355023, (6, 927): 433.39665255651784, (6, 948): 436.4428673600357, (6, 961): 435.53608164728234, (6, 962): 435.4430935647196, (6, 963): 435.46075295168725, (6, 967): 440.7989709287669, (6, 974): 440.8198341080117, (6, 998): 442.2727979469716, (6, 1014): 490.58626518515575, (6, 1086): 415.28285068766417, (6, 1087): 413.0717118688879, (6, 1089): 411.7553134484629, (6, 1090): 412.9652980266671, (6, 1092): 416.57681530691167, (6, 1097): 414.19633879277836, (6, 1107): 417.18059038749084, (6, 1387): 115.50357000052368, (6, 1554): 131.77007818079625, (6, 1827): 564.4374263732407, (6, 1828): 564.4562852624813, (6, 1829): 565.0176828410986, (6, 1830): 565.7961736117653, (6, 1831): 565.8137498112075, (6, 1832): 565.4255929875436, (6, 1833): 565.2535069760945, (6, 1836): 564.7318543013596, (6, 1841): 566.660972856454, (6, 1843): 565.9775190329441, (6, 1844): 566.4828804823125, (6, 1845): 565.8461018943908, (6, 1847): 562.6176108027531, (6, 1848): 563.5976074112489, (6, 1849): 568.3911090840802, (6, 1850): 568.6851864151656, (6, 1851): 564.886948821443, (6, 1852): 565.4251520102781, (6, 1854): 565.5242156440581, (6, 1856): 563.0982772140544, (6, 1857): 563.7862937047802, (6, 1858): 567.6209092009565, (6, 1861): 565.3589794589204, (6, 1866): 563.441239527564, (6, 1867): 566.3137269409414, (6, 1868): 565.3827365860271, (6, 1870): 567.0103248328682, (6, 1871): 565.7963441063142, (6, 1875): 565.1590691736086, (6, 1880): 563.2851986818126, (6, 1882): 564.2387342988894, (6, 1883): 568.190914069768, (6, 1889): 563.0022134625618, (6, 1893): 564.3049896300391, (6, 1894): 563.5168472192498, (6, 1899): 562.1043210076951, (6, 1900): 562.427079096361, (6, 1902): 565.4412758516477, (6, 1905): 566.5915555255098, (6, 1907): 563.7576408842709, (6, 1910): 563.4911233992187, (6, 1917): 566.8462643117955, (6, 1920): 563.408658166188, (6, 1935): 565.8092099053915, (6, 1937): 566.6819415216668, (6, 1946): 559.5928765888393, (6, 1949): 560.1430150432079, (6, 1950): 558.5577830324163, (6, 1951): 559.5804298624632, (6, 1952): 561.7900841782641, (6, 1953): 561.1024947422138, (6, 1954): 561.2956990115337, (6, 1958): 560.4250136586674, (6, 1960): 562.060623849396, (6, 1968): 562.7032415736634, (6, 1969): 565.0667053348687, (6, 1974): 564.5296005005131, (6, 1975): 564.8239451157195, (6, 1979): 562.3697357460625, (6, 1980): 563.1366734086743, (6, 1981): 563.1036536372975, (6, 1985): 563.2957153562006, (6, 1994): 559.6085509065797, (6, 2011): 564.5180694306787, (6, 2019): 572.3228528725239, (6, 2020): 571.2978712797127, (6, 2029): 568.2982209074398, (6, 2030): 570.5730437825711, (6, 2032): 568.2698910524515, (6, 2033): 569.4112407960095, (6, 2034): 569.8337953918757, (6, 2036): 568.5591270648601, (6, 2037): 568.8119351162908, (6, 2038): 566.9642221367441, (6, 2042): 577.3389714077587, (6, 2050): 568.2879911471526, (6, 2051): 568.6249139836415, (6, 2053): 568.6864903485006, (6, 2054): 569.6207466456489, (6, 2066): 567.8052539498889, (6, 2067): 567.5620316921132, (6, 2071): 557.6433519651064, (6, 2072): 558.9709180608712, (6, 2073): 553.0913811215119, (6, 2074): 553.1730595533284, (6, 2080): 551.1150303152767, (6, 2082): 559.796397887068, (6, 2083): 560.4539992462531, (6, 2089): 558.2802845200995, (6, 2090): 558.8111086374367, (6, 2092): 557.4468582671393, (6, 2098): 551.5695521244893, (6, 2099): 552.8258944679843, (6, 2101): 551.8226307039095, (6, 2102): 555.7849358376219, (6, 2103): 554.7128095080246, (6, 2104): 554.3295772522831, (6, 2106): 561.222248423641, (6, 2112): 552.7493952062143, (6, 2113): 556.6133120072374, (6, 2114): 558.3118704988132, (6, 2117): 562.199590614463, (6, 2123): 539.3033946311971, (6, 2124): 540.1252028989472, (6, 2134): 538.9102956140077, (6, 2138): 540.8763982988322, (6, 2141): 538.8481239018112, (6, 2148): 544.4275945016622, (6, 2150): 537.0592834291443, (6, 2151): 538.2440654013236, (6, 2152): 536.903672855394, (6, 2153): 544.2861392694347, (6, 2154): 540.6123779530484, (6, 2155): 540.9648283545599, (6, 2156): 539.8006842353934, (6, 2157): 543.3794021822737, (6, 2160): 544.1286230523115, (6, 2161): 537.1967973972812, (6, 2162): 546.094799724343, (6, 2163): 544.7946343638421, (6, 2164): 544.9849602649817, (6, 2168): 539.6389984333659, (6, 2172): 542.4198200795707, (6, 2174): 538.6955143453396, (6, 2178): 543.6847660824096, (6, 2179): 543.3210240509289, (6, 2183): 541.3251885978164, (6, 2185): 541.646907424058, (6, 2186): 540.8477560038864, (6, 2190): 543.8118779642169, (6, 2192): 542.4662059338095, (6, 2193): 541.4047186805536, (6, 2194): 540.0319322329675, (6, 2195): 540.4127091923467, (6, 2197): 543.0443104595942, (6, 2205): 541.9444152084733, (6, 2207): 540.333893258147, (6, 2208): 541.3501177934315, (6, 2212): 540.5384526535274, (6, 2214): 523.4337267467529, (6, 2225): 528.2176492501012, (6, 2231): 509.5852087214606, (6, 2278): 545.008212743183, (6, 2284): 548.6655164072163, (6, 2285): 548.6769214767686, (6, 2291): 545.9161879669734, (6, 2292): 543.3698631146362, (6, 2307): 546.986310060417, (6, 2313): 546.2624722904444, (6, 2317): 540.1108321881078, (6, 2319): 544.6079625857146, (6, 2321): 546.3664390755076, (6, 2323): 545.3239249250081, (6, 2326): 548.4372478672518, (6, 2327): 547.2579631770911, (6, 2329): 546.5435068363716, (6, 2330): 545.9364342014256, (6, 2332): 548.2891518424562, (6, 2344): 544.0238665264071, (6, 2346): 544.5803164299467, (6, 2361): 539.0277212983293, (6, 2368): 555.7321745327258, (6, 2374): 557.5041791383882, (6, 2375): 557.6382057940301, (6, 2377): 552.6239324934347, (6, 2378): 558.7223493252825, (6, 2379): 559.4473049580376, (6, 2380): 559.4681404151637, (6, 2383): 553.4753785848957, (6, 2385): 553.9710037071925, (6, 2395): 553.5099446047138, (6, 2397): 559.1765059327597, (6, 2398): 551.0943021494654, (6, 2399): 552.4721172793226, (6, 2400): 552.0871213182534, (6, 2402): 556.4273675696699, (6, 2403): 557.503422558377, (6, 2404): 557.5311773143039, (6, 2405): 555.1624728937406, (6, 2407): 556.7304714571401, (6, 2408): 558.25177483412, (6, 2409): 555.785644836741, (6, 2411): 558.5085580877205, (6, 2412): 557.8463380871335, (6, 2413): 558.8678124216913, (6, 2414): 557.5712404838046, (6, 2422): 558.534876419635, (6, 2424): 557.927661507671, (6, 2426): 557.9545284358069, (6, 2433): 556.3550603949202, (6, 2436): 556.4890070842631, (6, 2437): 550.0676321597252, (6, 2440): 551.301093707075, (6, 2445): 584.2989215515837, (6, 2447): 580.3439888142143, (6, 2454): 583.5095606172625, (6, 2455): 583.2035022629507, (6, 2460): 574.020721863414, (6, 2461): 575.2590987036523, (6, 2471): 597.4866478916022, (6, 2492): 595.8413748022483, (6, 2511): 583.057064298169, (6, 2523): 589.6653304523232, (6, 2525): 589.2597495687248, (6, 2535): 581.6628703144543, (6, 2537): 579.857665985809, (6, 2538): 580.6194982505336, (6, 2539): 582.3946929434908, (6, 2540): 582.5430722445946, (6, 2542): 584.6849759173759, (6, 2559): 609.0836830362408, (6, 2575): 609.2341524634776, (6, 2599): 558.2755702959716, (6, 2600): 569.768288416489, (6, 2607): 561.2954627328036, (6, 2627): 597.426024034483, (6, 2647): 604.5900629610475, (6, 2674): 599.1476058418642, (6, 2681): 599.6405202191331, (6, 2683): 601.770843576779, (6, 2686): 598.0597044295133, (6, 2689): 635.3116126434696, (6, 2690): 635.7888558807819, (6, 2713): 651.8042885211951, (6, 2714): 653.6413293741922, (6, 2715): 654.4683553656932, (6, 2739): 653.3724071487886, (6, 2740): 644.7232317485963, (6, 2741): 644.8927916518346, (6, 2749): 653.523427804619, (6, 2750): 653.3464867937561, (6, 2752): 653.7393070826804, (6, 2755): 654.6712335289527, (6, 2758): 654.8465695500659, (6, 2759): 654.6532672230115, (6, 2769): 653.1906695384544, (6, 2771): 646.9573517028743, (6, 2779): 650.3986706334746, (6, 2784): 642.3600560523386, (6, 2800): 647.193209020701, (6, 2802): 644.8029348085233, (6, 2803): 644.0854218627832, (6, 2804): 643.3667765130767, (6, 2805): 646.7132965022147, (6, 2807): 646.257217366913, (6, 2809): 646.8456049214607, (6, 2812): 640.431237056306, (6, 2814): 649.2334002099144, (6, 2817): 653.0286834111319, (6, 2819): 645.3790748227917, (6, 2823): 644.447769940028, (6, 2832): 648.3292520419024, (6, 2836): 644.4832290327736, (6, 2839): 645.8357513810214, (6, 2841): 651.386541347932, (6, 2843): 650.4566113606492, (6, 2846): 646.8704951397465, (6, 2849): 649.6095049294206, (6, 2852): 648.4781682663962, (6, 2853): 650.1550708772144, (6, 2876): 652.4211463137248, (6, 2877): 655.7824136464055, (6, 2885): 660.5328917920974, (6, 2918): 643.2356127708916, (6, 2921): 645.0509245874986, (6, 2925): 635.2267184441047, (6, 2926): 631.1976775026076, (6, 2930): 642.3657902604716, (6, 2931): 636.9168470050757, (6, 2938): 643.9539053093232, (6, 2940): 644.5422903960375, (6, 2947): 639.0813549764933, (6, 2949): 640.7376867158106, (6, 2950): 642.030139615267, (6, 2952): 641.3884869050745, (6, 2958): 640.9750104481685, (6, 2959): 640.8137957618053, (6, 2960): 642.5567728581153, (6, 2961): 642.1644835673288, (6, 2963): 640.8145307027629, (6, 2968): 641.6465436208263, (6, 2976): 640.2189347412608, (6, 2981): 632.7334291296135, (6, 2982): 633.2075478564777, (6, 2984): 632.7585339757878, (6, 3003): 632.5538197234823, (6, 3046): 614.6929636201448, (6, 3050): 625.7765950963259, (6, 3051): 625.9672279947899, (6, 3053): 624.9031318119683, (6, 3069): 634.1727818896674, (6, 3071): 622.6662288452968, (6, 3080): 661.9279081149589, (6, 3199): 635.551932674205, (6, 3200): 634.6542036807781, (6, 3205): 643.1818575878971, (6, 3209): 635.510606362343, (6, 3215): 634.2841946295869, (6, 3217): 632.6159962862189, (6, 3249): 633.9520746382477, (6, 3263): 646.3792983347731, (6, 3289): 636.6366090432588, (6, 3301): 638.2327266250309, (6, 3302): 637.1902971364847, (6, 3307): 636.3130043722128, (6, 3310): 638.9538035839541, (6, 3391): 663.3983279672422, (6, 3509): 354.70980811639777, (6, 3510): 353.6660190169794, (6, 3511): 353.6223478356508, (6, 3512): 352.3293171293586, (6, 3514): 351.9628546725515, (6, 3519): 360.7662104301023, (6, 3536): 355.2586399166476, (6, 3545): 356.16393713873936, (6, 3548): 353.5871377401509, (6, 3572): 356.74968964481894, (6, 3581): 357.93590546062666, (6, 3583): 354.18991687876036, (6, 3601): 363.8745180619649, (6, 3656): 364.982039247868, (6, 3669): 369.0110909511208, (6, 3670): 370.20121393136014, (6, 3695): 362.35086981275964, (6, 3696): 362.97513824968274, (6, 3782): 341.1594817143043, (6, 3792): 341.95475675007646, (6, 3989): 451.64900427061644, (6, 4008): 459.22368751834216, (6, 4031): 461.26355370493445, (6, 4045): 456.1625782025891, (6, 4144): 454.18487611239306, (6, 4145): 443.95645654979523, (6, 4164): 450.6414642441763, (6, 4168): 447.05341612212044, (6, 4173): 445.9585654905843, (6, 4181): 441.34902407233574, (6, 4228): 439.7743492306505, (6, 4248): 434.12073526752994, (6, 4254): 380.65429846574574, (6, 4260): 382.150416378372, (6, 4262): 383.95218242110093, (6, 4273): 384.22951968992237, (6, 4319): 351.6092662133194, (6, 4326): 351.0826416046702, (6, 4328): 351.8133830539541, (6, 4334): 352.3083134465693, (6, 4335): 351.42301728217024, (6, 4372): 199.0171679748853, (6, 4413): 215.10260295348067, (6, 4434): 199.11671750201086, (6, 4447): 204.16126211045392, (6, 4452): 198.95474951757475, (6, 4463): 144.57007405470094, (6, 4465): 146.91614339224023, (6, 4619): 210.45487519670948, (6, 4645): 216.59112282232294, (6, 4657): 214.94533042540425, (6, 4666): 212.2149200026529, (6, 4676): 215.81212114311418, (6, 4678): 217.0060134981325, (6, 4689): 213.57552547746616, (6, 4704): 231.34839898416607, (6, 4726): 260.521930220774, (6, 4727): 259.8725850967336, (6, 4730): 258.65819851832333, (6, 4731): 258.7349482095272, (6, 4734): 261.01471616445974, (6, 4735): 260.16595710885605, (6, 4736): 260.2638767994237, (6, 4737): 258.900560832813, (6, 4738): 258.87703742115997, (6, 4756): 259.39505875311426, (6, 4760): 257.38377875660785, (6, 4761): 258.2388685846643, (6, 4762): 256.2185248052675, (6, 4765): 257.54783410698514, (6, 4773): 262.0269881207405, (6, 4774): 261.0555314631836, (6, 4790): 261.65332821061855, (6, 4795): 261.1849639337306, (6, 4799): 261.1330630114734, (6, 4801): 261.98916809310407, (6, 4804): 261.90353469652723, (6, 4805): 261.51704674710305, (6, 4806): 260.2382586324612, (6, 4815): 259.2734190056784, (6, 4816): 261.0926659605048, (6, 4817): 260.9880928819774, (6, 4826): 260.13567095100547, (6, 4830): 259.01466382803824, (6, 4839): 259.20739495304616, (6, 4840): 259.5710362630291, (6, 4841): 258.06070664616357, (6, 4846): 257.7010699741189, (6, 4848): 257.1417910122911, (6, 4850): 257.65172474246634, (6, 4871): 252.37239942002796, (6, 4883): 257.2949219132126, (6, 4900): 255.37079297113596, (6, 4901): 254.24482321068604, (6, 4917): 199.53695562567387, (6, 4931): 194.69127917467154, (6, 4944): 200.46640655747893, (6, 4956): 195.19085446063366, (6, 4958): 194.29722925798904, (6, 4959): 192.86158250338895, (6, 4961): 196.48075030383555, (6, 4966): 193.56844709617187, (6, 5207): 188.160684907653, (6, 5272): 168.26475686174098, (6, 5283): 168.11354218441025, (6, 5287): 164.22090832282774, (6, 5289): 164.0609979158105, (6, 5293): 171.95811308811793, (6, 5295): 172.1146078413189, (6, 5296): 169.83101640761058, (6, 5298): 168.55741394697512, (6, 5303): 166.73242143797282, (6, 5305): 163.75545237029672, (6, 5306): 160.45687238746606, (6, 5307): 163.55294635522998, (6, 5308): 163.01367314584897, (6, 5313): 165.93020099467148, (6, 5314): 166.8207759838608, (6, 5317): 161.50790123157853, (6, 5319): 166.0483001297139, (6, 5324): 167.7263375560523, (6, 5326): 168.95401598438536, (6, 5348): 158.45622130993942, (6, 5351): 155.24586935401595, (6, 5399): 160.86390631300324, (6, 5413): 150.31891409214805, (6, 5422): 163.19740185204867, (6, 5445): 161.8032526796728, (6, 5448): 161.64788202156052, (6, 5456): 159.19071602005718, (6, 5467): 158.70105663087466, (6, 5624): 166.69297302201485, (6, 5671): 203.08371412631865, (6, 5672): 202.71466098828597, (6, 5797): 212.41442424762337, (6, 5871): 148.48880892496382, (6, 5976): 140.04434044061858, (6, 6118): 541.9327582744168, (6, 6248): 584.0624980004557, (6, 6345): 291.85927357152246, (6, 6352): 293.3703029996366, (6, 6354): 290.7583730046257, (6, 6359): 291.82079312940925, (6, 6376): 296.4091096256725, (6, 6378): 291.0796511707778, (6, 6381): 292.8661516387222, (6, 6383): 291.6314230604557, (6, 6396): 298.332428815779, (6, 6399): 293.4590988938154, (6, 6408): 291.96564812248175, (6, 6409): 287.68971873898545, (6, 6419): 284.6466730219882, (6, 6422): 288.95989518392054, (6, 6423): 288.8854132936869, (6, 6424): 286.90910862742874, (6, 6439): 286.03108347451126, (6, 6464): 285.3123069142758, (6, 6465): 286.67789025355574, (6, 6469): 289.0790200746141, (6, 6470): 289.7635774649232, (6, 6472): 291.8830319519091, (6, 6480): 286.2731612347445, (6, 6486): 279.2825984106423, (6, 6497): 281.31766466431475, (6, 6503): 278.0512891944884, (6, 6508): 281.8337891929599, (6, 6509): 279.80774800872985, (6, 6521): 283.4652511072926, (6, 6544): 279.8495455909169, (6, 6552): 282.360306834238, (6, 6553): 282.19423375064815, (6, 6554): 282.0783201650325, (6, 6578): 283.1862301694473, (6, 6582): 279.2586951256795, (6, 6601): 282.43526027175113, (6, 6609): 287.0920897693665, (6, 6610): 286.2985645214995, (6, 6611): 288.4157962478886, (6, 6614): 289.6382464770928, (6, 6615): 288.91696859973047, (6, 6616): 286.2493985326869, (6, 6617): 287.1833538236802, (6, 6618): 284.5068168266806, (6, 6619): 289.17446224862795, (6, 6620): 284.94168996711386, (6, 6621): 284.6233908459008, (6, 6622): 285.54236933201344, (6, 6623): 288.208601643637, (6, 6624): 286.79912730165796, (6, 6625): 287.49626813751837, (6, 6626): 289.7422779856895, (6, 6627): 290.76726600019373, (6, 6628): 283.59581162956437, (6, 6629): 285.20356546244494, (6, 6630): 289.5550838206439, (6, 6632): 285.92640776415976, (6, 6634): 288.67606280909314, (6, 6635): 285.31414532676814, (6, 6636): 285.7989737360382, (6, 6637): 284.9977317708105, (6, 6638): 288.31650216862823, (6, 6639): 290.01072400431514, (6, 6640): 288.98425946879775, (6, 6641): 283.595294147921, (6, 6642): 287.446657971469, (6, 6643): 290.6667902146712, (6, 6645): 288.5867887761357, (6, 6646): 285.51875299830465, (6, 6647): 287.94285159854104, (6, 6653): 289.31703052573005, (6, 6655): 290.43496522060883, (6, 6658): 288.1622598599189, (6, 6662): 286.50832891116835, (6, 6819): 270.2377665232179, (6, 6996): 249.11048920795596, (6, 7059): 249.7671125458906, (6, 7187): 204.3406850844992, (6, 7304): 231.78945725885612, (6, 7528): 229.84199060236378, (6, 7720): 256.0977742383062, (6, 7793): 248.75770716333673, (6, 7807): 251.2862165969289, (6, 7808): 247.05548489405317, (6, 7831): 278.5807090459553, (6, 7850): 286.64101292127646, (6, 7852): 288.0553880057668, (6, 8012): 265.0160266932033, (6, 8125): 220.321635114331, (6, 8208): 261.4543841474402, (6, 8392): 259.4403745543125, (6, 8651): 276.52982573084216, (6, 9088): 296.1082233479593, (6, 9443): 218.99725086652572, (6, 9444): 217.40424638233193, (6, 9828): 217.5748860092573, (6, 9868): 242.058625153872, (6, 10180): 217.60358725876802, (6, 10256): 226.53578157397675, (6, 10276): 227.3529614719582, (6, 10378): 246.40176809777182, (6, 10676): 187.06247599307622, (6, 10714): 174.04193050814357, (6, 10730): 195.91878384356906, (6, 10862): 24.0, (6, 10881): 28.009898925134888, (6, 10883): 27.442011534979013, (6, 10885): 24.0, (6, 10891): 26.600886858754414, (6, 10909): 26.27875941844676, (6, 10911): 27.128414517974768, (6, 10913): 25.982638877773756, (6, 10915): 26.064755180190645, (6, 10919): 26.836732497629743, (6, 11037): 24.0, (6, 11039): 24.0, (6, 11516): 554.7733147575783, (6, 11856): 352.84555120827287, (6, 11857): 349.85134037964536, (6, 11861): 351.33331400725234, (6, 11881): 353.10852670296157, (6, 11902): 349.22437894867596, (6, 11911): 350.6403655405344, (6, 11914): 350.2526549883424, (6, 11922): 352.3992650572689, (6, 11924): 353.8570979375273, (6, 11926): 352.8616421011547, (6, 11950): 357.38050236895776, (6, 11963): 360.72434553163464, (6, 11983): 362.0136332550102, (6, 11985): 362.22447096098784, (6, 12009): 364.6816654274711, (6, 12010): 361.51661444115615, (6, 12018): 362.337243829137, (6, 12020): 362.53406186214835, (6, 12021): 363.27907641913765, (6, 12024): 365.59046009845144, (6, 12025): 364.1662639916472, (6, 12027): 363.77715650532696, (6, 12031): 361.0964395154815, (6, 12032): 361.39714633929935, (6, 12035): 365.25265546425004, (6, 12041): 360.67758581821903, (6, 12045): 332.75900087810584, (6, 12145): 350.21020827489264, (6, 12275): 460.1806322906611, (6, 12294): 457.0717732185766, (6, 12358): 480.6667919978089, (6, 12463): 492.09797569760667, (6, 12465): 492.05897067200516, (6, 12482): 492.5800306002088, (6, 12503): 492.8386084340362, (6, 12506): 493.71499677175433, (6, 12549): 488.2884086233711, (6, 12559): 488.32680307111787, (6, 12569): 490.296399712005, (6, 12572): 490.88219402493235, (6, 12574): 489.2688341060244, (6, 12576): 488.62194537448636, (6, 12591): 486.43179955607593, (6, 12608): 490.2146307382103, (6, 12696): 480.4408471788106, (6, 12710): 482.65739687470125, (6, 12728): 483.15149615369376, (6, 12766): 350.3615385603717, (6, 12771): 335.89970157933277, (6, 12790): 335.5121198507197, (6, 12795): 335.785715973393, (6, 12797): 323.0704289674583, (6, 12798): 323.6780604315115, (6, 12811): 329.98426089744544, (6, 12830): 329.60130375727846, (6, 12848): 327.1644218863151, (6, 12850): 325.5715266990478, (6, 12852): 328.2463828334212, (6, 12854): 327.3136235795001, (6, 12859): 327.17770392654035, (6, 12861): 323.9059245244905, (6, 12865): 332.69581571802985, (6, 12866): 331.1725631733854, (6, 12867): 334.0056722813803, (6, 12874): 332.7747668568439, (6, 12875): 333.0511014306209, (6, 12881): 331.30654851332525, (6, 12883): 332.3491793269555, (6, 12885): 333.91224064513267, (6, 12888): 331.12586643541994, (6, 12889): 330.18567895646044, (6, 12892): 333.3759477828982, (6, 12893): 331.88108132597176, (6, 12896): 331.7178226742264, (6, 12906): 335.99604574964025, (6, 13018): 346.8571421732144, (6, 13071): 351.15370860615946, (6, 13131): 327.89205925054733, (6, 13146): 329.6480879826642, (6, 13159): 344.5957843339766, (6, 13193): 325.63813449684756, (6, 13198): 309.7745605923314, (6, 13292): 317.6993367619052, (6, 13296): 313.10551645313797, (6, 13406): 317.242437126889, (6, 13407): 317.9941999230245, (6, 13417): 325.32004644742506, (6, 13418): 327.3665313245281, (6, 13438): 324.4175435667537, (6, 13442): 322.4675869136506, (6, 13443): 322.17296758853666, (6, 13764): 356.5761996185708, (6, 13766): 356.40468865804627, (6, 13771): 359.63771992619655, (6, 13783): 351.59381066312454, (6, 13784): 354.90196752719055, (6, 13792): 364.5933748891827, (6, 13824): 352.3361511941948, (6, 14017): 333.4344836966364, (6, 14870): 44.62905957761995, (6, 14997): 200.80227021039366, (6, 15000): 199.08551228705676, (6, 15003): 197.36579070584318, (6, 15006): 204.95773772077925, (6, 15007): 204.7943198750123, (6, 15056): 199.64443873541734, (6, 15063): 198.6175667369852, (6, 15069): 196.65918352377437, (6, 15076): 203.5794213633886, (6, 15086): 205.76110642590282, (6, 15087): 203.35817758636767, (6, 15111): 205.1591203800562, (6, 15116): 203.9392530722717, (6, 15722): 208.6416871759477, (6, 15998): 169.75035233557432, (6, 16073): 500.08418603212704, (6, 16939): 505.2865561682162, (6, 16940): 503.3645775014645, (6, 16951): 507.29980629660304, (6, 16963): 507.05260105977675, (6, 16965): 508.62308758887457, (6, 16969): 509.1528710052838, (6, 16970): 507.28135623768605, (6, 16971): 505.8033773588227, (6, 16973): 506.33447074342087, (6, 16974): 509.85752400327306, (6, 16976): 506.99782370334674, (6, 16978): 505.69679124805253, (6, 16980): 507.00987310729494, (6, 16982): 510.5020179345569, (6, 17045): 610.3879049162974, (6, 17048): 612.7107325335069, (6, 17304): 420.02567860670445, (6, 17305): 420.7901834832583, (6, 17330): 421.2542728815415, (6, 17334): 417.53992492889824, (6, 17343): 423.2417403832014, (6, 17345): 419.4222282291773, (6, 17347): 422.37867188319046, (6, 17351): 414.6233342425703, (6, 17372): 418.0428157335549, (6, 17373): 422.8174503923111, (6, 17377): 423.3125668948489, (6, 17382): 420.6168164870623, (6, 17383): 420.46236306874215, (6, 17389): 419.0305194779933, (6, 17400): 421.4535734890258, (6, 17401): 421.08977559656114, (6, 17402): 421.8015185587688, (6, 17403): 422.22872913420844, (6, 17440): 421.704686477014, (6, 17455): 424.0562371147486, (6, 17491): 425.7511708591244, (6, 17507): 411.3756853185472, (6, 17509): 412.30064250900404, (6, 17590): 415.8654693312884, (6, 17615): 395.25773327232787, (6, 17642): 397.6847630663309, (6, 17643): 398.3281750260426, (6, 17668): 394.7177495528104, (6, 17721): 387.0199169021135, (6, 17754): 399.1952470295212, (6, 17769): 409.59774460330823, (6, 17776): 407.5703257641178, (6, 17804): 411.5508774191478, (6, 17809): 412.9682244664508, (6, 17824): 410.79671713761724, (6, 17837): 412.5348042718166, (6, 17838): 413.79811228550705, (6, 17862): 413.2831090450643, (6, 17866): 415.7490740333897, (6, 17872): 411.6015085238012, (6, 17873): 409.97630508006, (6, 17881): 412.63779563801586, (6, 17947): 337.52316446279013, (6, 17951): 335.7720759018362, (6, 17953): 334.7388929168199, (6, 17954): 334.4024227168484, (6, 17959): 338.36156229378616, (6, 17963): 338.9625300062337, (6, 18000): 328.33351276146794, (6, 18001): 327.7178499848265, (6, 18111): 328.7684129318162, (6, 18148): 266.7267693399418, (6, 18166): 285.62204122655237, (6, 18189): 312.6032844775884, (6, 18239): 422.7986116787695, (6, 18240): 422.99335343718997, (6, 18245): 423.0407353224171, (6, 18247): 422.95573787296956, (6, 18251): 423.29290477357966, (6, 18256): 423.9047939939837, (6, 18258): 423.6708819562266, (6, 18259): 423.84887997017444, (6, 18260): 424.1463143420097, (6, 18262): 424.5560782264963, (6, 18263): 424.1185956047863, (6, 18264): 424.40092627681935, (6, 18266): 424.8496863052636, (6, 18267): 425.0960511814296, (6, 18268): 425.29602952822574, (6, 18269): 425.8093936602499, (6, 18275): 425.5681586306059, (6, 18285): 424.2215540536478, (6, 18308): 418.8251028561324, (6, 18313): 417.59294623705244, (6, 18314): 418.8181360347043, (6, 18315): 425.19953491354863, (6, 18316): 425.4467022281354, (6, 18317): 425.7046496354273, (6, 18320): 425.538238138026, (6, 18321): 425.8076009690729, (6, 18322): 426.1565638387264, (6, 18324): 426.0380011858601, (6, 18325): 426.7312185969799, (6, 18326): 426.4599360184034, (6, 18327): 426.1769795965322, (6, 18329): 426.7273752050854, (6, 18330): 427.2586531901203, (6, 18331): 426.65611103863574, (6, 18332): 426.18121652952937, (6, 18333): 426.9355095218791, (6, 18336): 426.1242992587886, (6, 18337): 426.17953992675115, (6, 18403): 427.41413441164394, (6, 18432): 426.1729941858274, (6, 18451): 427.0624410933865, (6, 18466): 427.1301921608518, (6, 18481): 424.62963893549835, (6, 18483): 424.82994837563405, (6, 18484): 424.2945882227065, (6, 18485): 422.47746027508174, (6, 18486): 422.7803787872624, (6, 18487): 421.6462378091797, (6, 18489): 423.35935346767127, (6, 18490): 423.69724133875997, (6, 18491): 424.11504532116413, (6, 18492): 420.92385746878267, (6, 18493): 422.38976974980125, (6, 18494): 423.35326201905383, (6, 18495): 423.3555677892499, (6, 18496): 423.083976441434, (6, 18497): 421.1968818826129, (6, 18498): 422.2277686852503, (6, 18499): 422.95452475475906, (6, 18501): 422.06980060383574, (6, 18502): 421.5812849767801, (6, 18503): 421.45411702163125, (6, 18504): 423.5066999230575, (6, 18506): 421.5545048065926, (6, 18507): 420.9723943057297, (6, 18508): 422.6564313445612, (6, 18509): 422.4730495480998, (6, 18510): 421.1816229825166, (6, 18511): 422.1147021025684, (6, 18512): 421.9537626913383, (6, 18515): 423.2626230680586, (6, 18516): 422.6311076944456, (6, 18517): 421.72217740638746, (6, 18518): 423.19166038167685, (6, 18519): 423.72344535529527, (6, 18520): 422.7621982912672, (6, 18522): 426.0651860764384, (6, 18523): 425.9397981272765, (6, 18532): 426.2423558438359, (6, 18535): 425.38707384509536, (6, 18537): 424.9111958185536, (6, 18539): 424.89511934651176, (6, 18540): 424.8282720695788, (6, 18541): 424.9614840016831, (6, 18542): 425.06718195615025, (6, 18543): 424.45182416128904, (6, 18546): 424.36762009617064, (6, 18555): 425.0933614072378, (6, 18556): 425.074323750107, (6, 18565): 425.88874060065524, (6, 18567): 425.66578597596276, (6, 18568): 425.45575235755376, (6, 18577): 428.3993003460301, (6, 18583): 428.51434503088655, (6, 18605): 429.8655680024447, (6, 18608): 425.02834033742306, (6, 18616): 432.57866620683455, (6, 18618): 434.5072928777857, (6, 18625): 435.32883850037945, (6, 18645): 433.9306230365707, (6, 18646): 433.9365593326415, (6, 18653): 430.4471761456634, (6, 18654): 432.254805050597, (6, 18655): 430.7334284674046, (6, 18666): 441.04020104559186, (6, 18837): 455.84803610246854, (6, 18974): 432.10573038030515, (6, 18999): 436.7711404274667, (6, 19000): 437.5378514981301, (6, 19174): 417.24696131412605, (6, 19342): 436.7443589413088, (6, 19455): 411.46781004502753, (6, 19555): 385.01548377082, (6, 19564): 394.39370074453234, (6, 19573): 391.35951904223936, (6, 19586): 389.5256722388199, (6, 19605): 388.89263827567765, (6, 19611): 390.6642749492842, (6, 19614): 387.8496409866861, (6, 19641): 408.70938655631693, (6, 19702): 410.59651194646, (6, 19713): 408.59311799480423, (6, 19731): 368.4669193649355, (6, 19819): 410.4117539546365, (6, 19893): 263.34212061161406, (6, 19899): 264.8661087390991, (6, 19929): 265.40367237501914, (6, 19951): 274.96269227103545, (6, 19962): 262.8859870976513, (6, 19970): 271.47777077305193, (6, 19971): 270.0013018411469, (6, 19972): 268.10877432207485, (6, 19975): 268.8105295091224, (6, 19978): 283.77044534270937, (6, 19987): 284.937914727927, (6, 19989): 282.066856250402, (6, 20039): 285.9563857498514, (6, 20043): 288.551673259649, (6, 20047): 288.8131305723347, (6, 20052): 284.51913297700673, (6, 20054): 284.111576214237, (6, 20085): 308.4480252715336, (6, 20104): 309.7652964330847, (6, 20132): 300.45024089571217, (6, 20203): 248.73444176971563, (6, 20280): 243.1005001446428, (6, 20285): 240.92821577772605, (6, 20290): 244.4780995945591, (6, 20297): 243.8436483867833, (6, 20309): 274.3535093088096, (6, 20453): 301.849983615641, (6, 20485): 239.77468403059936, (6, 20520): 238.7248237526588, (6, 20526): 233.01901383056426, (6, 20698): 414.7718067988959, (6, 20868): 439.24595413950186, (6, 21042): 283.7874799813357, (6, 21057): 293.49627880310265, (6, 21066): 286.454897406017, (6, 21075): 287.8798276896186, (6, 21093): 281.3597227567641, (6, 21098): 283.6879672255839, (6, 21127): 282.8980811006116, (6, 21130): 283.16518604286136, (6, 21144): 285.8535862295111, (6, 21146): 282.2927077786057, (6, 21147): 286.5818821271773, (6, 21148): 287.19506376137997, (6, 21153): 294.88906909534217, (6, 21293): 295.8649153203053, (6, 21426): 321.3226841079374, (6, 21442): 336.5767004191522, (6, 21451): 337.9289340714283, (6, 21466): 327.4294758809317, (6, 21469): 328.3457405764717, (6, 21471): 327.028144918476, (6, 21473): 327.44649901649615, (6, 21475): 326.70143587930244, (6, 21482): 330.03824664741427, (6, 21484): 329.26120783264577, (6, 21488): 329.0237510604015, (6, 21494): 325.1468424111917, (6, 21498): 326.2235827652296, (6, 21500): 323.29724118052957, (6, 21514): 320.11637040641773, (6, 21537): 319.574614326152, (6, 21662): 317.2357279015695, (6, 21691): 312.19167976793085, (6, 21757): 315.4031178112604, (6, 21777): 256.4107704690351, (6, 21778): 255.32263477267458, (6, 21779): 254.3857087327112, (6, 21790): 259.3134812053417, (6, 21802): 256.2457410179585, (6, 21824): 255.88305391899974, (6, 21874): 252.77602466817234, (6, 21879): 249.29557916365943, (6, 21983): 269.48890095637336, (6, 22002): 272.043710897386, (6, 22132): 298.78301213284743, (6, 22261): 182.1948670696983, (6, 22298): 176.494954622228, (6, 22339): 181.07260359285348, (6, 22508): 166.1612796661591, (6, 22841): 705.803646097222, (6, 22842): 705.39991019436, (6, 22874): 699.5107515552352, (6, 22941): 701.3767540199574, (6, 22956): 703.7511551435786, (6, 22960): 705.5476899143783, (6, 22968): 702.5752315733097, (6, 22970): 704.1445029122706, (6, 22974): 701.9032010771747, (6, 22980): 705.1469307904894, (6, 23025): 699.6209928326942, (6, 23028): 697.8169557698783, (6, 23081): 696.7799228089325, (6, 23104): 681.8844770261634, (6, 23147): 668.3296079912733, (6, 23298): 335.98462391852803, (6, 23376): 331.3273449265022, (6, 23381): 322.10706854663704, (6, 23529): 333.767921738604, (6, 23556): 331.8570263991748, (6, 23718): 338.4609148420293, (6, 24001): 365.572625141842, (6, 24094): 364.4050049750552, (6, 24129): 369.34662557666286, (6, 24174): 355.0572179060612, (6, 24235): 363.38387862695066, (6, 24259): 370.76449709465174, (6, 24260): 370.00883331779806, (6, 24261): 369.31741736039936, (6, 24305): 377.55278512164074, (6, 24306): 377.99373324084, (6, 24307): 376.8419618186137, (6, 24308): 384.41547806410534, (6, 24498): 397.95100727000283, (6, 24499): 397.8764408954741, (6, 24500): 397.1496424214416, (6, 24668): 400.78631791151264, (6, 24711): 400.0326253054354, (6, 24756): 400.07209396063854, (6, 24788): 402.9036263768252, (6, 24809): 394.0082020635248, (6, 24813): 397.06233896487294, (6, 24821): 396.18536988622895, (6, 24825): 396.2904237860809, (6, 24832): 393.8411453628631, (6, 24833): 394.8847376892334, (6, 24835): 395.759621543193, (6, 24837): 397.8073098838681, (6, 24840): 393.48056175205664, (6, 24841): 395.5049424335875, (6, 24844): 393.2585838962992, (6, 24845): 395.2613134890502, (6, 24846): 393.6906268884343, (6, 24849): 394.1308135739991, (6, 24850): 397.05311592242003, (6, 24863): 384.5279856250324, (6, 24866): 386.4845266942283, (6, 24885): 387.78256053851277, (6, 24886): 387.356012092702, (6, 24889): 393.5469193678564, (6, 24903): 396.04889746209943, (6, 24909): 390.67739532555703, (6, 24999): 478.2219532705294, (6, 25019): 478.06546717401045, (6, 25028): 476.65049470628713, (6, 25137): 227.81450264640506, (6, 25145): 229.88668755977176, (6, 25208): 239.85772160210152, (6, 25233): 236.52029081738226, (6, 25371): 238.22021673294458, (6, 25377): 235.85173162568088, (6, 25828): 165.18488324628478, (6, 25851): 168.0783828181748, (6, 25874): 171.11786267705935, (6, 25898): 165.4429441914965, (6, 25946): 165.00457617743697, (6, 26047): 167.09953733496744, (6, 26066): 230.56713542293573, (6, 26197): 195.67932769478182, (6, 26212): 118.30690445357993, (6, 26253): 114.70246304955862, (6, 26254): 116.79417677462858, (6, 26257): 115.65761923996867, (6, 26258): 114.70654195718726, (6, 26260): 115.36480389678803, (6, 26266): 119.52053669199546, (6, 26267): 119.430537385105, (6, 26271): 118.7777684242874, (6, 26304): 135.1421828128911, (6, 26305): 136.7372888771122, (6, 26363): 151.95668976701808, (6, 26441): 133.5251160265762, (6, 26442): 133.92072328623303, (6, 26450): 131.76217826065857, (6, 26459): 128.18861648302988, (6, 26462): 126.98721377527092, (6, 26467): 132.9890279091285, (6, 26471): 132.9451078264788, (6, 26472): 133.25913296298668, (6, 26473): 133.66766259022484, (6, 26476): 137.6805478454265, (6, 26485): 130.85643647723043, (6, 26493): 132.66781182555175, (6, 26524): 126.35603452508911, (6, 26525): 127.0473637148915, (6, 26556): 131.96752648029178, (6, 26560): 128.98284045487276, (6, 26561): 127.03416582438078, (6, 26564): 132.1795264867823, (6, 26569): 127.64290211215095, (6, 26570): 128.20532660459224, (6, 26573): 130.03237936062968, (6, 26581): 131.32736917522504, (6, 26583): 130.0595711015675, (6, 26593): 133.04389518343365, (6, 26837): 134.74350052974845, (6, 26844): 135.56395902946204, (6, 26863): 137.06017362356076, (6, 26893): 140.64874680182746, (6, 26902): 141.90771134566424, (6, 26905): 137.78459848845077, (6, 26912): 139.67940294610216, (6, 26921): 138.5558538566136, (6, 26922): 140.99099541081154, (6, 27212): 89.81002301410165, (6, 27218): 85.88560753930837, (6, 27239): 93.78258213377522, (6, 27257): 92.48264048148813, (6, 27274): 94.8457474647355, (6, 27279): 95.0804158796305, (6, 27282): 92.92350840108678, (6, 27283): 92.52956440456344, (6, 27285): 96.21018853340844, (6, 27286): 95.35487873691731, (6, 27290): 91.20321611316193, (6, 27295): 88.89496887704973, (6, 27300): 94.9751892257325, (6, 27344): 92.25376010311892, (6, 27366): 95.30306992793876, (6, 27383): 97.74196328814844, (6, 27398): 98.86262352011498, (6, 27406): 96.22769011490925, (6, 27407): 96.39102142699717, (6, 27426): 89.57545844339683, (6, 27432): 81.14160575864689, (6, 27460): 85.83975489091164, (6, 27523): 107.9275845409876, (6, 27545): 134.31787131673343, (6, 27602): 191.37476176845277, (6, 27606): 191.86000552559216, (6, 27646): 146.84991622148019, (6, 27667): 157.2978019206425, (6, 27672): 157.36343240890162, (6, 27674): 155.87060270282538, (6, 27688): 155.47988107395676, (6, 27692): 159.7436919007588, (6, 27693): 158.26734680424772, (6, 27705): 158.74314863549853, (6, 27712): 159.93967950111895, (6, 27786): 183.53300651089398, (6, 27790): 174.90900842235345, (6, 27791): 174.11014415522104, (6, 27795): 180.5670797945174, (6, 27801): 174.21457477357234, (6, 27813): 185.5837259480777, (6, 27816): 182.99591216958405, (6, 27823): 173.9603513538981, (6, 27830): 179.92197232763252, (6, 27884): 136.54193248560225, (6, 27885): 143.44691730030104, (6, 27896): 138.76353662406962, (6, 27919): 137.8407234556236, (6, 27922): 139.61562305599173, (6, 27930): 136.67619414829275, (6, 27934): 137.49749267178527, (6, 27935): 138.3363975977068, (6, 27948): 207.2104659151631, (6, 27951): 202.2123630018278, (6, 28061): 248.00823508870855, (6, 28290): 318.2462298914275, (6, 28292): 322.6873107280092, (6, 28293): 319.3125040450338, (6, 28295): 320.1266825655015, (6, 28296): 319.0083503616912, (6, 28297): 316.0659367974756, (6, 28302): 316.83871149517415, (6, 28310): 481.7741161219124, (6, 28313): 486.6851868953652, (6, 28372): 480.45428210788276, (6, 28398): 481.0999347221632, (6, 28399): 480.87386546348836, (6, 28400): 482.09169607689853, (6, 28401): 478.075826616031, (6, 28445): 487.68707566908336, (6, 28475): 471.03800791662604, (6, 28885): 347.0662857973493, (6, 28886): 345.4681917073722, (6, 28915): 343.4687078975504, (6, 28916): 343.59109025955905, (6, 28917): 342.49630351276636, (6, 28921): 349.35945838485554, (6, 28931): 348.37610066005726, (6, 28945): 334.4888921871478, (6, 28982): 338.7029676871241, (6, 29219): 328.89592433489344, (6, 29228): 325.5595438391897, (6, 29246): 340.6977376652813, (6, 29248): 337.69819015506977, (6, 29282): 333.7983095649608, (6, 29290): 345.68106831628256, (6, 29291): 344.03149647270897, (6, 29292): 345.1928091763702, (6, 29293): 343.5270685498495, (6, 29294): 343.71826467962154, (6, 29298): 342.94515507778215, (6, 29299): 342.08422254458696, (6, 29304): 342.1232977521715, (6, 29317): 339.136307469659, (6, 29323): 338.98957746923264, (6, 29330): 340.29096751131436, (6, 29331): 341.548834461031, (6, 29344): 323.6374669643955, (6, 29445): 274.07299341080227, (6, 29724): 713.8843031017265, (6, 29738): 714.7184353527741, (6, 29745): 712.8657806837729, (6, 29748): 716.284934053464, (6, 29750): 718.8842925180961, (6, 29759): 714.7804963783038, (6, 29772): 717.9133796964716, (6, 29781): 717.3135284227915, (6, 29784): 715.5173106743838, (6, 29790): 718.5123436643973, (6, 29811): 718.0286743060218, (6, 29817): 731.4272541236772, (6, 29818): 730.8908584772606, (6, 29929): 710.7375140936507, (6, 30039): 713.4057901216136, (6, 30066): 701.5868409187435, (6, 30116): 679.6620564140088, (6, 30238): 646.9413586931187, (6, 30248): 654.4772957252128, (6, 30260): 654.0916316209965, (6, 30545): 343.83327253992434, (6, 30733): 314.4875144368337, (6, 30756): 289.25763255587805, (6, 30921): 311.8396456300251, (6, 31079): 331.7367490260096, (6, 31149): 313.69528826212485, (6, 31154): 316.19902052408037, (6, 31160): 313.1567732901589, (6, 31163): 315.7351892684017, (6, 31189): 298.81684826357935, (6, 31215): 302.0796774980105, (6, 31259): 311.72231201078256, (6, 31262): 309.3813272093348, (6, 31430): 340.2425092472989, (6, 31568): 326.216465607289, (6, 31751): 330.0585745403336, (8, 109): 368.0482789905721, (8, 872): 810.4197023441922, (8, 873): 812.8155008223534, (8, 877): 811.8365623157125, (8, 879): 812.1841063731971, (8, 884): 809.5965457674689, (8, 889): 811.1363088659551, (8, 891): 808.8257461062906, (8, 892): 814.0578099430047, (8, 894): 813.7883034355708, (8, 896): 811.6125088404519, (8, 903): 811.8343972971201, (8, 909): 808.0176365541076, (8, 910): 809.0506915593867, (8, 912): 807.4482167062412, (8, 913): 805.6555889408564, (8, 916): 805.0036623173975, (8, 926): 809.9329542592118, (8, 927): 809.1442759151778, (8, 948): 807.9705393251903, (8, 961): 809.6756211631933, (8, 962): 809.9990133696906, (8, 963): 810.345832906105, (8, 967): 812.8800285480331, (8, 974): 811.4050546425261, (8, 998): 813.7612110171202, (8, 1014): 867.0984414954954, (8, 1086): 806.4525191228953, (8, 1087): 806.3506395738806, (8, 1089): 804.0202869585993, (8, 1090): 805.0205889506886, (8, 1092): 808.4966766026788, (8, 1097): 805.805344348256, (8, 1107): 810.3546312441698, (8, 1387): 442.5101436757531, (8, 1554): 404.21722161965033, (8, 1827): 917.5055041538984, (8, 1828): 917.8118295683626, (8, 1829): 918.1419721579765, (8, 1830): 917.513955507206, (8, 1831): 917.7726972285797, (8, 1832): 917.540073949615, (8, 1833): 917.6118572797383, (8, 1836): 917.3850093704729, (8, 1841): 918.8510292208482, (8, 1843): 918.2104158104129, (8, 1844): 918.4529545180231, (8, 1845): 917.6527072498516, (8, 1847): 915.3095419360947, (8, 1848): 916.1443695814822, (8, 1849): 920.0137033053804, (8, 1850): 920.4631741082466, (8, 1851): 916.6690787142501, (8, 1852): 916.6311900802316, (8, 1854): 917.1094901347291, (8, 1856): 915.0601112360858, (8, 1857): 916.03342680284, (8, 1858): 919.7022598908413, (8, 1861): 918.0042247877241, (8, 1866): 914.9210678686017, (8, 1867): 918.9786892215576, (8, 1868): 918.5449457532028, (8, 1870): 918.2542740996955, (8, 1871): 918.9454859404179, (8, 1875): 917.1339932187741, (8, 1880): 915.6730465723648, (8, 1882): 915.7794847775028, (8, 1883): 920.6086087681682, (8, 1889): 916.276670331474, (8, 1893): 918.3481992965029, (8, 1894): 917.7769906752449, (8, 1899): 915.8155828088486, (8, 1900): 916.2902786258333, (8, 1902): 919.3874386997369, (8, 1905): 920.0958733781919, (8, 1907): 916.81896520112, (8, 1910): 917.2248486572588, (8, 1917): 922.0405449731226, (8, 1920): 916.963248050817, (8, 1935): 920.3893088684365, (8, 1937): 921.0158171793619, (8, 1946): 914.7031691329352, (8, 1949): 915.4922982654721, (8, 1950): 912.649964839078, (8, 1951): 913.9686702022636, (8, 1952): 914.6581879349789, (8, 1953): 915.2974579340098, (8, 1954): 914.537157291852, (8, 1958): 915.1783692470236, (8, 1960): 916.375211172981, (8, 1968): 916.8480072828755, (8, 1969): 920.7276891085423, (8, 1974): 919.6965717469474, (8, 1975): 919.6245887047932, (8, 1979): 917.9496324171056, (8, 1980): 917.6246053011287, (8, 1981): 918.265583409324, (8, 1985): 918.7492425398818, (8, 1994): 911.2077476648404, (8, 2011): 915.6833817033327, (8, 2019): 921.6740306878469, (8, 2020): 920.8806701420966, (8, 2029): 917.6828135051279, (8, 2030): 920.3337086687637, (8, 2032): 917.0639778926572, (8, 2033): 918.856512917823, (8, 2034): 918.7333512318872, (8, 2036): 915.1756997542246, (8, 2037): 916.101849770897, (8, 2038): 916.8160967466956, (8, 2042): 926.2632595980215, (8, 2050): 918.5670081649481, (8, 2051): 918.3299262798747, (8, 2053): 918.6250146480545, (8, 2054): 919.457590621827, (8, 2066): 917.7455419772709, (8, 2067): 917.8024886288965, (8, 2071): 909.6776856363109, (8, 2072): 911.323731287877, (8, 2073): 907.249378884959, (8, 2074): 906.9752105207235, (8, 2080): 904.1602550811566, (8, 2082): 912.1895853258267, (8, 2083): 913.0466300864036, (8, 2089): 911.3819305671822, (8, 2090): 912.1975433250342, (8, 2092): 911.210307150019, (8, 2098): 905.3013669072403, (8, 2099): 906.1659390199219, (8, 2101): 905.0530384549502, (8, 2102): 909.4741318370202, (8, 2103): 908.0505538245064, (8, 2104): 907.2330256836018, (8, 2106): 913.5615584580553, (8, 2112): 905.5641621136854, (8, 2113): 910.0528455235195, (8, 2114): 910.9756142884121, (8, 2117): 914.1507404758213, (8, 2123): 910.7332706877706, (8, 2124): 911.645158386053, (8, 2134): 908.8690210793098, (8, 2138): 911.623502787915, (8, 2141): 909.2399809368462, (8, 2148): 909.8644385140295, (8, 2150): 906.9876062058785, (8, 2151): 907.8963868554781, (8, 2152): 906.4362020119923, (8, 2153): 910.2415047918062, (8, 2154): 906.5093540256543, (8, 2155): 905.95179296228, (8, 2156): 905.3368900040747, (8, 2157): 905.8413594526645, (8, 2160): 912.5622209712191, (8, 2161): 906.2097933862439, (8, 2162): 910.1228941755471, (8, 2163): 908.8670100379028, (8, 2164): 908.7363722403396, (8, 2168): 906.9964469503751, (8, 2172): 907.5180738593333, (8, 2174): 907.6984478544529, (8, 2178): 908.1678855240762, (8, 2179): 907.5504461387371, (8, 2183): 911.4813354052038, (8, 2185): 911.4959496661706, (8, 2186): 910.7908429248688, (8, 2190): 912.8178107588906, (8, 2192): 911.5336261070419, (8, 2193): 911.7608450501714, (8, 2194): 910.4484250236686, (8, 2195): 910.1670246427353, (8, 2197): 911.7694720431949, (8, 2205): 909.8019968789004, (8, 2207): 907.2703415415632, (8, 2208): 908.6676869009095, (8, 2212): 912.3431486032032, (8, 2214): 884.1752666990604, (8, 2225): 887.0578107291905, (8, 2231): 882.8126456684417, (8, 2278): 899.5072620880945, (8, 2284): 902.0409977311232, (8, 2285): 901.5899508832324, (8, 2291): 895.7231100457577, (8, 2292): 896.8955267414456, (8, 2307): 900.2654176978099, (8, 2313): 894.9003665649236, (8, 2317): 895.1259428963054, (8, 2319): 897.7704903496972, (8, 2321): 898.9178285908313, (8, 2323): 898.9179088113872, (8, 2326): 903.9563238719978, (8, 2327): 902.7843594085736, (8, 2329): 901.9677639081923, (8, 2330): 900.9993404797816, (8, 2332): 902.8536639166558, (8, 2344): 900.0977455796603, (8, 2346): 899.9305863638909, (8, 2361): 900.3934934399388, (8, 2368): 913.5455757743521, (8, 2374): 914.7489359560219, (8, 2375): 915.236407126723, (8, 2377): 910.8179755899404, (8, 2378): 916.000192875988, (8, 2379): 915.9998325288528, (8, 2380): 916.5246517943555, (8, 2383): 912.086020079579, (8, 2385): 912.8194386513361, (8, 2395): 912.9952999414653, (8, 2397): 915.4137877823991, (8, 2398): 909.3977794064992, (8, 2399): 911.0658237111924, (8, 2400): 910.7056757055595, (8, 2402): 912.9556552979304, (8, 2403): 913.9510457848106, (8, 2404): 914.254360610477, (8, 2405): 911.8132963992376, (8, 2407): 913.8696364242984, (8, 2408): 914.9894628015542, (8, 2409): 912.5715975544458, (8, 2411): 913.7519032194194, (8, 2412): 913.5629507113882, (8, 2413): 914.3530557017531, (8, 2414): 912.99938017695, (8, 2422): 913.3813602343503, (8, 2424): 913.8860697166655, (8, 2426): 914.1407870489428, (8, 2433): 912.2085930386534, (8, 2436): 911.5882451107403, (8, 2437): 905.804486343388, (8, 2440): 907.1135300918996, (8, 2445): 931.7505100983195, (8, 2447): 928.7090478782914, (8, 2454): 931.6893657370595, (8, 2455): 931.9568082268942, (8, 2460): 922.5662709466558, (8, 2461): 923.7031144904512, (8, 2471): 941.5969394193581, (8, 2492): 917.5236856647974, (8, 2511): 909.0599148061137, (8, 2523): 913.3746957866065, (8, 2525): 911.7154362010317, (8, 2535): 916.6125435359016, (8, 2537): 914.4864669798241, (8, 2538): 916.0709359913101, (8, 2539): 914.8860172121882, (8, 2540): 917.5622682551652, (8, 2542): 918.8979094223624, (8, 2559): 949.4982316734753, (8, 2575): 946.1458385479199, (8, 2599): 903.2019445124946, (8, 2600): 912.8064066856218, (8, 2607): 907.6771096380345, (8, 2627): 912.5340438107781, (8, 2647): 917.5132617679473, (8, 2674): 915.4363362132583, (8, 2681): 914.3380399513711, (8, 2683): 917.1425529769919, (8, 2686): 914.2668627784816, (8, 2689): 949.2970013163613, (8, 2690): 949.3840465870444, (8, 2713): 953.6348675262791, (8, 2714): 953.8709307435824, (8, 2715): 954.7577891967164, (8, 2739): 954.076831962104, (8, 2740): 949.4726666439425, (8, 2741): 949.9830255893431, (8, 2749): 952.4746630045959, (8, 2750): 952.8792104692195, (8, 2752): 953.5691056892155, (8, 2755): 954.1893328705637, (8, 2758): 953.8775520634, (8, 2759): 953.937969754523, (8, 2769): 953.0541397852517, (8, 2771): 950.6472446753095, (8, 2779): 950.0049416980355, (8, 2784): 939.6522071921357, (8, 2800): 940.511184130032, (8, 2802): 947.2742927485062, (8, 2803): 947.0517939615107, (8, 2804): 946.5061561054316, (8, 2805): 947.673964155081, (8, 2807): 947.7346365861722, (8, 2809): 947.1469267763172, (8, 2812): 941.7702290870437, (8, 2814): 946.0758553780161, (8, 2817): 945.212812792469, (8, 2819): 948.1325077725598, (8, 2823): 941.3162082654952, (8, 2832): 948.607477284319, (8, 2836): 944.645736055455, (8, 2839): 947.8391616791567, (8, 2841): 945.9471005635635, (8, 2843): 945.8414961287527, (8, 2846): 944.9576385606113, (8, 2849): 949.0293221268304, (8, 2852): 948.2041106724621, (8, 2853): 949.4019307350372, (8, 2876): 949.2568594278807, (8, 2877): 952.3537385558368, (8, 2885): 952.1869199932548, (8, 2918): 949.3122092443446, (8, 2921): 950.5438763152031, (8, 2925): 945.1158454106574, (8, 2926): 943.4988460851403, (8, 2930): 946.556000220656, (8, 2931): 945.401468422308, (8, 2938): 949.1329168139129, (8, 2940): 954.0201507807776, (8, 2947): 949.5963902575697, (8, 2949): 946.9602355146067, (8, 2950): 947.3814661849173, (8, 2952): 946.7020211346713, (8, 2958): 946.6500735900645, (8, 2959): 947.5221650633961, (8, 2960): 948.9486532661659, (8, 2961): 948.1399787709478, (8, 2963): 945.9675794054721, (8, 2968): 946.2814846092219, (8, 2976): 945.9053400223949, (8, 2981): 931.6698021900638, (8, 2982): 931.0653750659743, (8, 2984): 930.3421201221537, (8, 3003): 928.9065935597043, (8, 3046): 922.7536073381682, (8, 3050): 928.4206067095344, (8, 3051): 929.0371583844511, (8, 3053): 927.4635952523028, (8, 3069): 935.3430877388398, (8, 3071): 927.6259530775047, (8, 3080): 951.7986984329704, (8, 3199): 925.2765913200122, (8, 3200): 923.5497539288806, (8, 3205): 933.3406462945629, (8, 3209): 924.3412741899982, (8, 3215): 923.7773562092825, (8, 3217): 921.8128387994698, (8, 3249): 924.093157163383, (8, 3263): 938.9862924744751, (8, 3289): 929.145176657693, (8, 3301): 929.2808310793743, (8, 3302): 928.696898602001, (8, 3307): 927.8505042327704, (8, 3310): 930.1261763288137, (8, 3391): 925.1474720701459, (8, 3509): 622.4196487431844, (8, 3510): 621.0522836769475, (8, 3511): 622.1285261151294, (8, 3512): 621.427278487687, (8, 3514): 621.8452578531677, (8, 3519): 624.8123524852502, (8, 3536): 625.1233573818893, (8, 3545): 627.4362097777537, (8, 3548): 625.5531245783286, (8, 3572): 625.6995330248097, (8, 3581): 623.4889017061436, (8, 3583): 623.2405362301545, (8, 3601): 627.1213076085794, (8, 3656): 624.2557227271681, (8, 3669): 620.1703560403421, (8, 3670): 621.3358193586264, (8, 3695): 614.9269065159191, (8, 3696): 615.9199895700988, (8, 3782): 628.8175939398164, (8, 3792): 626.9002428968522, (8, 3989): 37.947210497921084, (8, 4008): 30.27016641213906, (8, 4031): 28.870815506256537, (8, 4045): 33.381799569159746, (8, 4144): 35.36018366509592, (8, 4145): 45.823381246680576, (8, 4164): 38.924779796236706, (8, 4168): 42.64926095518108, (8, 4173): 43.854913008970506, (8, 4181): 48.308924406437406, (8, 4228): 49.73498570733181, (8, 4248): 55.52430247119798, (8, 4254): 109.68161480826407, (8, 4260): 107.9306813739259, (8, 4262): 106.42333306151245, (8, 4273): 105.94146478794728, (8, 4319): 138.76191269564433, (8, 4326): 139.19435991914426, (8, 4328): 138.41128203374564, (8, 4334): 138.18670311282543, (8, 4335): 139.09328845733071, (8, 4372): 364.33127557554474, (8, 4413): 376.055821981357, (8, 4434): 362.4212445947068, (8, 4447): 357.83582703069345, (8, 4452): 363.30869578857016, (8, 4463): 389.43351557644195, (8, 4465): 387.5808157577108, (8, 4619): 393.3811592506296, (8, 4645): 390.7037050374122, (8, 4657): 392.80712057542286, (8, 4666): 394.7054686246001, (8, 4676): 394.59715331911264, (8, 4678): 393.5880171539138, (8, 4689): 396.13015229586983, (8, 4704): 396.3506105351157, (8, 4726): 444.515002108392, (8, 4727): 443.7877102949257, (8, 4730): 442.2410603874189, (8, 4731): 443.6013792773043, (8, 4734): 439.14441278636235, (8, 4735): 439.24873726526, (8, 4736): 440.2824582632036, (8, 4737): 439.9986570622531, (8, 4738): 440.71579528432005, (8, 4756): 441.86127628285516, (8, 4760): 434.36839443722505, (8, 4761): 433.2181654646164, (8, 4762): 434.33113541040933, (8, 4765): 435.18766939884716, (8, 4773): 445.1836002416361, (8, 4774): 445.79972974238683, (8, 4790): 444.5096686269845, (8, 4795): 443.5567123574293, (8, 4799): 446.7841784871241, (8, 4801): 450.0385281958653, (8, 4804): 442.21746260289484, (8, 4805): 441.45303550424734, (8, 4806): 447.38764810120955, (8, 4815): 447.8027530629809, (8, 4816): 449.049329567143, (8, 4817): 450.8619529515367, (8, 4826): 449.33022093499505, (8, 4830): 448.9184877515811, (8, 4839): 436.53766131343275, (8, 4840): 437.81094806043825, (8, 4841): 436.80409132897535, (8, 4846): 436.05777043831864, (8, 4848): 437.1615193003229, (8, 4850): 438.03002931461884, (8, 4871): 423.95639190898925, (8, 4883): 431.712446633816, (8, 4900): 425.92254059973885, (8, 4901): 426.05728380895886, (8, 4917): 417.7361575948411, (8, 4931): 414.88159528423336, (8, 4944): 417.1423039905056, (8, 4956): 416.31788537493486, (8, 4958): 418.0536823552906, (8, 4959): 418.7628807117152, (8, 4961): 416.1487984871123, (8, 4966): 416.6833417480222, (8, 5207): 413.8208375971104, (8, 5272): 323.64881282576533, (8, 5283): 324.3522603638475, (8, 5287): 329.6602343553092, (8, 5289): 330.1512106948457, (8, 5293): 319.7436588404971, (8, 5295): 321.14566714288645, (8, 5296): 323.66474480819153, (8, 5298): 325.0579229840926, (8, 5303): 327.6813278079746, (8, 5305): 328.2397791334276, (8, 5306): 331.4129391098465, (8, 5307): 328.19581025502634, (8, 5308): 329.2934691555756, (8, 5313): 326.09769410456045, (8, 5314): 325.46713159988667, (8, 5317): 330.94033976159966, (8, 5319): 327.75802949224686, (8, 5324): 325.5188667505308, (8, 5326): 323.9373006432874, (8, 5348): 333.4594052861849, (8, 5351): 337.3620154781933, (8, 5399): 334.1804885952472, (8, 5413): 343.6367089494372, (8, 5422): 331.96775865208195, (8, 5445): 331.8427797302578, (8, 5448): 331.393477511983, (8, 5456): 333.962588726904, (8, 5467): 335.0949497094976, (8, 5624): 322.80717617975597, (8, 5671): 304.1563635923166, (8, 5672): 302.7957130175384, (8, 5797): 320.8720447252113, (8, 5871): 367.30822206611407, (8, 5976): 360.5831698727232, (8, 6118): 776.0107522956071, (8, 6248): 801.1556073450473, (8, 6345): 305.7769941322032, (8, 6352): 311.76986756490436, (8, 6354): 304.46425437193125, (8, 6359): 303.0331278310462, (8, 6376): 310.2570133628637, (8, 6378): 305.1398318751572, (8, 6381): 303.34433514478474, (8, 6383): 307.1429719693397, (8, 6396): 303.08256319921105, (8, 6399): 305.4032143247511, (8, 6408): 311.78958305999623, (8, 6409): 309.64685470741625, (8, 6419): 320.31351020356465, (8, 6422): 311.5181740598676, (8, 6423): 312.036481575348, (8, 6424): 305.8316430557375, (8, 6439): 307.1946250125311, (8, 6464): 309.05232869417307, (8, 6465): 309.39821750027437, (8, 6469): 308.15676522582646, (8, 6470): 308.4081849663556, (8, 6472): 300.9183271519238, (8, 6480): 303.320726169646, (8, 6486): 301.2277231794441, (8, 6497): 301.9700263574019, (8, 6503): 310.16357591259856, (8, 6508): 308.92282539453754, (8, 6509): 308.16798211768827, (8, 6521): 303.14376924467604, (8, 6544): 304.34603635216075, (8, 6552): 311.7370784765068, (8, 6553): 312.73001374746246, (8, 6554): 313.7305100887087, (8, 6578): 309.96837849426123, (8, 6582): 311.48925259250115, (8, 6601): 309.68237473957186, (8, 6609): 301.05551475904014, (8, 6610): 300.94330146593205, (8, 6611): 300.33249707193596, (8, 6614): 300.5954426763602, (8, 6615): 300.55706635675773, (8, 6616): 300.08960223192474, (8, 6617): 300.33776483955756, (8, 6618): 299.48330560166835, (8, 6619): 301.3824318795717, (8, 6620): 300.3383386248546, (8, 6621): 301.2148323017374, (8, 6622): 300.8353646028756, (8, 6623): 300.95928629506, (8, 6624): 301.9637427272842, (8, 6625): 301.9792916600615, (8, 6626): 301.3201052046677, (8, 6627): 300.5837180880324, (8, 6628): 300.788846412225, (8, 6629): 302.058996245248, (8, 6630): 302.287442541945, (8, 6632): 301.9956337775666, (8, 6634): 303.34027649699027, (8, 6635): 301.36405849657143, (8, 6636): 300.1360672472045, (8, 6637): 303.218284883745, (8, 6638): 302.4232139221735, (8, 6639): 300.64135135935817, (8, 6640): 302.15742470714997, (8, 6641): 301.4507829398221, (8, 6642): 302.57292311491165, (8, 6643): 301.2394448010566, (8, 6645): 301.38090966789423, (8, 6646): 299.56276987279057, (8, 6647): 302.2297674634202, (8, 6653): 300.5169242429818, (8, 6655): 300.55185352225016, (8, 6658): 303.4991114377657, (8, 6662): 302.8047547201099, (8, 6819): 353.42699872734465, (8, 6996): 342.0273867231734, (8, 7059): 331.0969037607005, (8, 7187): 363.5341152336125, (8, 7304): 377.8672783489318, (8, 7528): 348.3579297101999, (8, 7720): 280.37804920543084, (8, 7793): 284.2844779791302, (8, 7807): 282.5623540764008, (8, 7808): 285.22295634997766, (8, 7831): 297.0307563532729, (8, 7850): 285.0547629410675, (8, 7852): 287.06442412774294, (8, 8012): 279.9895593553216, (8, 8125): 292.0649314345694, (8, 8208): 261.9325083269704, (8, 8392): 294.730304316743, (8, 8651): 407.8532785882941, (8, 9088): 353.3437137970876, (8, 9443): 448.399111636948, (8, 9444): 447.1414833524937, (8, 9828): 504.55307716854577, (8, 9868): 498.37705203533733, (8, 10180): 292.89579761960476, (8, 10256): 271.69063196781883, (8, 10276): 277.91015243885437, (8, 10378): 264.8222544421626, (8, 10676): 317.1990296624363, (8, 10714): 336.43862777924835, (8, 10730): 321.44144195975576, (8, 10862): 482.0107595614892, (8, 10881): 481.00752360235856, (8, 10883): 481.82036082024405, (8, 10885): 482.05445972500416, (8, 10891): 483.10079085696975, (8, 10909): 481.5148361453688, (8, 10911): 479.6560190005177, (8, 10913): 480.44259155256657, (8, 10915): 479.56783300328254, (8, 10919): 478.6836878928461, (8, 11037): 506.6714361133886, (8, 11039): 502.27448765331843, (8, 11516): 72.2232906255396, (8, 11856): 137.72412472404892, (8, 11857): 140.99001750839003, (8, 11861): 139.38200710372217, (8, 11881): 137.05106820170323, (8, 11902): 140.58545258987226, (8, 11911): 138.962175841467, (8, 11914): 139.44265406399614, (8, 11922): 137.58691122902482, (8, 11924): 136.14898387526628, (8, 11926): 137.03132317703094, (8, 11950): 132.44678249475103, (8, 11963): 129.4886270151073, (8, 11983): 127.5944944021289, (8, 11985): 128.2701795746379, (8, 12009): 125.26035683094594, (8, 12010): 128.2764587323284, (8, 12018): 127.44801928367758, (8, 12020): 127.36087385598653, (8, 12021): 126.6162106679386, (8, 12024): 124.56910869328622, (8, 12025): 125.98687441583732, (8, 12027): 126.28621159989865, (8, 12031): 128.66427001355197, (8, 12032): 128.4878445058079, (8, 12035): 124.5903375589667, (8, 12041): 130.2163086404842, (8, 12045): 158.5959747171199, (8, 12145): 139.67647336671052, (8, 12275): 31.608117078044742, (8, 12294): 39.70721715567434, (8, 12358): 24.0, (8, 12463): 24.0, (8, 12465): 24.0, (8, 12482): 24.0, (8, 12503): 24.0, (8, 12506): 24.0, (8, 12549): 24.0, (8, 12559): 24.0, (8, 12569): 24.0, (8, 12572): 24.0, (8, 12574): 24.0, (8, 12576): 24.0, (8, 12591): 24.0, (8, 12608): 24.0, (8, 12696): 24.0, (8, 12710): 24.0, (8, 12728): 24.0, (8, 12766): 205.5243763294553, (8, 12771): 214.23269947681104, (8, 12790): 215.48796593357747, (8, 12795): 218.41528096779004, (8, 12797): 230.32580794219083, (8, 12798): 228.68501452380116, (8, 12811): 219.11509267838966, (8, 12830): 222.31940257860174, (8, 12848): 220.67932914726487, (8, 12850): 219.9377711020748, (8, 12852): 222.77251561941662, (8, 12854): 224.2398037682714, (8, 12859): 219.24151540239816, (8, 12861): 227.07232548302983, (8, 12865): 217.31619157226078, (8, 12866): 218.0672706480828, (8, 12867): 215.13350497926228, (8, 12874): 216.5557302346882, (8, 12875): 215.44486083151017, (8, 12881): 219.99976432905336, (8, 12883): 218.18609193540058, (8, 12885): 214.48270425720602, (8, 12888): 219.02264140373458, (8, 12889): 219.4326860816719, (8, 12892): 216.24377092527465, (8, 12893): 218.95980268182848, (8, 12896): 218.08209623214654, (8, 12906): 216.51125911655078, (8, 13018): 231.26900163481105, (8, 13071): 231.81145570916647, (8, 13131): 241.50697371188673, (8, 13146): 231.7434397737086, (8, 13159): 247.15019818906552, (8, 13193): 243.3211081131853, (8, 13198): 260.1623501699033, (8, 13292): 240.7589183903748, (8, 13296): 235.6237526062053, (8, 13406): 270.8664982224162, (8, 13407): 271.4649705675947, (8, 13417): 273.271794372157, (8, 13418): 271.5720592628722, (8, 13438): 263.689736699142, (8, 13442): 262.0685770585482, (8, 13443): 263.50889284224405, (8, 13764): 394.7596254791959, (8, 13766): 392.8999696534924, (8, 13771): 395.30592105897387, (8, 13783): 395.3824422876262, (8, 13784): 390.6246976073409, (8, 13792): 399.8265570673493, (8, 13824): 396.7661206324137, (8, 14017): 383.129149679316, (8, 14870): 446.6176763335832, (8, 14997): 372.5384863087857, (8, 15000): 372.84460644659015, (8, 15003): 372.20010879854715, (8, 15006): 367.5866095307134, (8, 15007): 366.49151725399474, (8, 15056): 368.0612500044108, (8, 15063): 369.36095289597705, (8, 15069): 370.2966495529558, (8, 15076): 366.64224105074226, (8, 15086): 369.63952287334774, (8, 15087): 371.51579898797445, (8, 15111): 374.4989702077646, (8, 15116): 372.8296922024444, (8, 15722): 403.03694275199206, (8, 15998): 435.595629172754, (8, 16073): 658.0756621616789, (8, 16939): 837.8228160466117, (8, 16940): 836.0925880310481, (8, 16951): 837.6805985696794, (8, 16963): 837.9415321935454, (8, 16965): 840.2149989479148, (8, 16969): 839.4632790678992, (8, 16970): 838.8388083126447, (8, 16971): 836.8044275568483, (8, 16973): 836.5302958151129, (8, 16974): 840.9971384363322, (8, 16976): 839.0832384564611, (8, 16978): 837.6449702276185, (8, 16980): 839.9512683634855, (8, 16982): 840.837430702566, (8, 17045): 889.8782589061944, (8, 17048): 892.4119776450503, (8, 17304): 69.81113859341266, (8, 17305): 68.75796306732227, (8, 17330): 68.39356324898814, (8, 17334): 72.21258552518815, (8, 17343): 66.4388659282486, (8, 17345): 70.11149857392242, (8, 17347): 67.1438062773307, (8, 17351): 74.98502020035932, (8, 17372): 71.5998687004351, (8, 17373): 66.89720152564729, (8, 17377): 66.38524251312802, (8, 17382): 68.98781182253376, (8, 17383): 69.23825971793075, (8, 17389): 70.59421699803299, (8, 17400): 68.31976346487406, (8, 17401): 68.73101702770711, (8, 17402): 67.95009198007067, (8, 17403): 67.5109469400956, (8, 17440): 67.76418748163616, (8, 17455): 65.47689604925114, (8, 17491): 63.71916184183614, (8, 17507): 79.23143029860836, (8, 17509): 78.62042137847565, (8, 17590): 73.60287977282427, (8, 17615): 95.77902638918827, (8, 17642): 93.23833043195351, (8, 17643): 92.37166567974901, (8, 17668): 96.45386251742416, (8, 17721): 105.09161548939059, (8, 17754): 96.34921179712744, (8, 17769): 81.76331326794602, (8, 17776): 82.29408237676877, (8, 17804): 80.30596313964388, (8, 17809): 79.14366426153725, (8, 17824): 81.65743318185775, (8, 17837): 77.51175895005531, (8, 17838): 76.05660083566906, (8, 17862): 76.43136849050751, (8, 17866): 74.24472127492812, (8, 17872): 78.15126987524677, (8, 17873): 79.60124790005527, (8, 17881): 77.2164632970059, (8, 17947): 697.4175370013934, (8, 17951): 693.8956898045138, (8, 17953): 693.2903811102277, (8, 17954): 693.5808329829341, (8, 17959): 696.5778025936748, (8, 17963): 695.2171652497578, (8, 18000): 677.486185587482, (8, 18001): 678.2857592528676, (8, 18111): 730.4523727558866, (8, 18148): 642.3522521926817, (8, 18166): 676.7943122246517, (8, 18189): 708.2076504904974, (8, 18239): 67.07997254834224, (8, 18240): 66.84447142001827, (8, 18245): 66.82614278315295, (8, 18247): 66.84972245691378, (8, 18251): 66.52623741283487, (8, 18256): 65.88582924461713, (8, 18258): 66.07830137476371, (8, 18259): 65.88582589987502, (8, 18260): 65.57132418046908, (8, 18262): 65.15333050308253, (8, 18263): 65.6571906202143, (8, 18264): 65.35887428492344, (8, 18266): 64.83750630937566, (8, 18267): 64.58191643184283, (8, 18268): 64.36657977209718, (8, 18269): 63.8329967565957, (8, 18275): 64.08352642910825, (8, 18285): 65.55763452554021, (8, 18308): 71.26144142892922, (8, 18313): 72.47532167094394, (8, 18314): 71.11844587663968, (8, 18315): 64.52750321633118, (8, 18316): 64.23868181312605, (8, 18317): 63.96813390941676, (8, 18320): 64.18267708384056, (8, 18321): 63.886672610481114, (8, 18322): 63.52575310334608, (8, 18324): 63.69531082629436, (8, 18325): 63.02477965562941, (8, 18326): 63.289613673442055, (8, 18327): 63.45357272049284, (8, 18329): 63.095123055873486, (8, 18330): 62.40975203621992, (8, 18331): 63.01904438027926, (8, 18332): 63.48047446890807, (8, 18333): 62.767444835469774, (8, 18336): 63.63343490634826, (8, 18337): 63.617369454960446, (8, 18403): 62.15296860272131, (8, 18432): 64.79024882082572, (8, 18451): 62.443628642387125, (8, 18466): 63.25102745218817, (8, 18481): 65.23413879908577, (8, 18483): 64.99647245942167, (8, 18484): 65.54555108232037, (8, 18485): 67.44480205190999, (8, 18486): 67.34852360040863, (8, 18487): 68.49450465291008, (8, 18489): 66.61023540470535, (8, 18490): 66.44006741732609, (8, 18491): 66.04491781903504, (8, 18492): 69.13213305746515, (8, 18493): 67.78983298903113, (8, 18494): 66.57509267553216, (8, 18495): 66.77244340167492, (8, 18496): 66.98255226462823, (8, 18497): 68.99208825137318, (8, 18498): 67.78071620605088, (8, 18499): 67.06819018207001, (8, 18501): 68.02290137736169, (8, 18502): 68.50687789655052, (8, 18503): 68.57533683889217, (8, 18504): 66.51228369282268, (8, 18506): 68.68142202537904, (8, 18507): 69.28771378303568, (8, 18508): 67.40819037739337, (8, 18509): 67.63621165140385, (8, 18510): 68.91170144380261, (8, 18511): 68.17404315778333, (8, 18512): 68.2228881759047, (8, 18515): 66.82233157293612, (8, 18516): 67.61817306806314, (8, 18517): 68.5960267309308, (8, 18518): 67.0220516125089, (8, 18519): 66.27216896911082, (8, 18520): 67.2457565394817, (8, 18522): 63.88898020868924, (8, 18523): 64.06521772658758, (8, 18532): 63.85500648567739, (8, 18535): 64.57384494881877, (8, 18537): 64.9815604513258, (8, 18539): 65.03469776677909, (8, 18540): 65.13495598696443, (8, 18541): 65.05951640166897, (8, 18542): 64.98737345710704, (8, 18543): 65.46409162630768, (8, 18546): 65.69490100301968, (8, 18555): 65.10304463660943, (8, 18556): 65.18743915806719, (8, 18565): 64.2716150272354, (8, 18567): 64.65077590289627, (8, 18568): 64.7316672570901, (8, 18577): 62.42411358945991, (8, 18583): 61.9920461905145, (8, 18605): 60.5540600507361, (8, 18608): 65.60365603920562, (8, 18616): 58.54999396540316, (8, 18618): 57.59408396970295, (8, 18625): 55.77663376923084, (8, 18645): 56.413472390678564, (8, 18646): 56.70099642634741, (8, 18653): 60.22735882630681, (8, 18654): 58.960897202834815, (8, 18655): 60.23476150004889, (8, 18666): 51.35467212931116, (8, 18837): 46.88618619747124, (8, 18974): 58.42130705086834, (8, 18999): 54.42160592832247, (8, 19000): 53.51488851731825, (8, 19174): 99.92863615570558, (8, 19342): 81.72614545580056, (8, 19455): 91.00107044500227, (8, 19555): 140.35691448802277, (8, 19564): 138.6075862621803, (8, 19573): 140.39290736762453, (8, 19586): 141.11994998389036, (8, 19605): 140.13028581332654, (8, 19611): 138.82327135476478, (8, 19614): 139.12136034773366, (8, 19641): 115.87186312477391, (8, 19702): 116.85631973873153, (8, 19713): 118.39388919374603, (8, 19731): 148.45348478843752, (8, 19819): 98.24210719941264, (8, 19893): 230.47116930414754, (8, 19899): 233.62248454001735, (8, 19929): 229.0499105379187, (8, 19951): 228.42437713327348, (8, 19962): 232.99527241667465, (8, 19970): 224.24443436534546, (8, 19971): 226.182377393385, (8, 19972): 227.7427546439567, (8, 19975): 226.45960969352853, (8, 19978): 219.242787581908, (8, 19987): 217.86277924485006, (8, 19989): 217.91357817001796, (8, 20039): 217.20198795350655, (8, 20043): 215.32233582103635, (8, 20047): 213.59953535296998, (8, 20052): 215.22948403771647, (8, 20054): 216.1026135293492, (8, 20085): 204.33302428653224, (8, 20104): 204.10625774838178, (8, 20132): 207.78381050047517, (8, 20203): 248.33900087659475, (8, 20280): 254.37787682255686, (8, 20285): 256.8757277579425, (8, 20290): 253.13306515982723, (8, 20297): 252.92497094541721, (8, 20309): 233.98791906607505, (8, 20453): 221.99469338407445, (8, 20485): 252.82515917244058, (8, 20520): 252.62913326226837, (8, 20526): 258.6743242770113, (8, 20698): 459.2647381155907, (8, 20868): 525.4612842364437, (8, 21042): 229.16245916397767, (8, 21057): 216.04428070428642, (8, 21066): 223.46502561873692, (8, 21075): 224.51221089304155, (8, 21093): 229.5522652310273, (8, 21098): 222.47657730090174, (8, 21127): 228.80682780906605, (8, 21130): 227.02925427046256, (8, 21144): 226.09018087424968, (8, 21146): 229.65392710074696, (8, 21147): 225.9299013658983, (8, 21148): 224.1077749125279, (8, 21153): 225.07454652411255, (8, 21293): 209.4172664263229, (8, 21426): 202.63050421153716, (8, 21442): 187.5552873411249, (8, 21451): 186.13932888015822, (8, 21466): 195.4091045205992, (8, 21469): 193.46294329430216, (8, 21471): 196.38455928834117, (8, 21473): 194.84817289933545, (8, 21475): 196.303146121206, (8, 21482): 191.98697171053482, (8, 21484): 192.5214612845039, (8, 21488): 193.59719400753616, (8, 21494): 196.66789326039518, (8, 21498): 195.13041080276116, (8, 21500): 197.85870510598474, (8, 21514): 195.42308870185823, (8, 21537): 199.19895819089632, (8, 21662): 194.99172955689122, (8, 21691): 202.77384434357586, (8, 21757): 213.61702794518456, (8, 21777): 258.61057966839405, (8, 21778): 260.5055632861871, (8, 21779): 260.1630083262965, (8, 21790): 255.71159243440513, (8, 21802): 257.21294079852856, (8, 21824): 255.9914920265873, (8, 21874): 260.5742096339598, (8, 21879): 263.065347334179, (8, 21983): 247.95681212101755, (8, 22002): 232.45332497847846, (8, 22132): 231.77148554158777, (8, 22261): 531.7111800432277, (8, 22298): 528.4071621485785, (8, 22339): 554.4605633307676, (8, 22508): 491.5490129535781, (8, 22841): 899.1362243296015, (8, 22842): 899.3671610565546, (8, 22874): 895.2358854380144, (8, 22941): 894.9861828008093, (8, 22956): 898.1614290117203, (8, 22960): 898.5114996324186, (8, 22968): 904.4386336676414, (8, 22970): 904.8345329920214, (8, 22974): 908.1450809941227, (8, 22980): 911.7562348122339, (8, 23025): 913.9688696869631, (8, 23028): 913.6852394837798, (8, 23081): 922.8404364010503, (8, 23104): 920.3935288765095, (8, 23147): 881.5880264479509, (8, 23298): 164.5958089541352, (8, 23376): 170.3755178872466, (8, 23381): 177.1172545095973, (8, 23529): 163.68911830647616, (8, 23556): 166.53830066426895, (8, 23718): 165.74884784736201, (8, 24001): 129.88253925542307, (8, 24094): 126.46027947252828, (8, 24129): 121.08687181853986, (8, 24174): 135.48709080165872, (8, 24235): 126.20220394688423, (8, 24259): 118.8465434103575, (8, 24260): 119.5863392093986, (8, 24261): 120.3422234670323, (8, 24305): 111.96882207696746, (8, 24306): 111.4930511928321, (8, 24307): 112.6799062935635, (8, 24308): 112.17045419889959, (8, 24498): 91.72675710584718, (8, 24499): 91.77903467591253, (8, 24500): 92.56498267081442, (8, 24668): 92.09157724498074, (8, 24711): 89.5247280995615, (8, 24756): 90.10702443568583, (8, 24788): 87.14996556305695, (8, 24809): 96.15625442298075, (8, 24813): 93.01875106212405, (8, 24821): 93.9005145845865, (8, 24825): 93.8910174340281, (8, 24832): 96.25252288261298, (8, 24833): 95.24830731882098, (8, 24835): 94.44533721029524, (8, 24837): 92.39150189905871, (8, 24840): 96.64222507998618, (8, 24841): 94.605302078748, (8, 24844): 96.91504631740956, (8, 24845): 94.76262830522283, (8, 24846): 96.60120100724897, (8, 24849): 96.21236094178235, (8, 24850): 93.09956549592229, (8, 24863): 105.02386768775676, (8, 24866): 103.0845970002275, (8, 24885): 101.90011878136575, (8, 24886): 102.39341837184199, (8, 24889): 96.07036038897378, (8, 24903): 93.51849347736683, (8, 24909): 98.79034672830282, (8, 24999): 24.0, (8, 25019): 24.0, (8, 25028): 24.0, (8, 25137): 278.04085972757247, (8, 25145): 276.73741936041887, (8, 25208): 286.5017711316619, (8, 25233): 288.6290420216608, (8, 25371): 263.3304774856883, (8, 25377): 262.7417797822288, (8, 25828): 332.496032847938, (8, 25851): 338.81976388723155, (8, 25874): 328.37399737676105, (8, 25898): 329.7784344945779, (8, 25946): 333.37384052909294, (8, 26047): 322.4610287440378, (8, 26066): 258.9191114906492, (8, 26197): 294.0483312394492, (8, 26212): 396.6806589023834, (8, 26253): 403.121422470896, (8, 26254): 400.2109002017506, (8, 26257): 399.4237361023912, (8, 26258): 402.2509988274791, (8, 26260): 400.68704449177835, (8, 26266): 399.82999750313957, (8, 26267): 398.48140893484873, (8, 26271): 398.8251926090881, (8, 26304): 374.70598458421017, (8, 26305): 373.8406032769081, (8, 26363): 345.0014100727543, (8, 26441): 547.322122581871, (8, 26442): 546.6549451174232, (8, 26450): 543.3992316466034, (8, 26459): 543.1399944430833, (8, 26462): 543.5919794971, (8, 26467): 553.1461744258932, (8, 26471): 550.4713112974518, (8, 26472): 550.1883977981302, (8, 26473): 550.0791132347204, (8, 26476): 548.5530652136173, (8, 26485): 544.7643167670788, (8, 26493): 544.8655473923924, (8, 26524): 545.0210592317761, (8, 26525): 544.6489359802359, (8, 26556): 549.1790820178448, (8, 26560): 548.8564890269415, (8, 26561): 546.7891471985969, (8, 26564): 548.2989561112116, (8, 26569): 546.2895314899384, (8, 26570): 545.4710818047214, (8, 26573): 546.0035977791075, (8, 26581): 545.937008137576, (8, 26583): 545.2183092701849, (8, 26593): 545.9703340373487, (8, 26837): 553.8033905004061, (8, 26844): 555.9813304092525, (8, 26863): 551.2604605488601, (8, 26893): 557.5381074541033, (8, 26902): 560.4972031872235, (8, 26905): 557.48301701682, (8, 26912): 559.7989475775196, (8, 26921): 554.2663082656467, (8, 26922): 548.3604023247881, (8, 27212): 566.918260507652, (8, 27218): 564.13901993244, (8, 27239): 571.1633705520995, (8, 27257): 569.0128439529508, (8, 27274): 572.0444099997454, (8, 27279): 571.6211714365708, (8, 27282): 569.1351847910958, (8, 27283): 570.0257653997476, (8, 27285): 573.1980011707282, (8, 27286): 570.9998229330034, (8, 27290): 567.0177632139826, (8, 27295): 565.4163438672028, (8, 27300): 572.4546971938051, (8, 27344): 566.0060697014894, (8, 27366): 568.8631865468828, (8, 27383): 573.5104857712885, (8, 27398): 576.4318588201423, (8, 27406): 573.92535804772, (8, 27407): 574.6218595230349, (8, 27426): 571.025463817727, (8, 27432): 560.374683248347, (8, 27460): 566.9984179063304, (8, 27523): 570.309224337639, (8, 27545): 613.6853903546305, (8, 27602): 670.5291977513474, (8, 27606): 671.512124687177, (8, 27646): 613.1381146891816, (8, 27667): 624.4650368340953, (8, 27672): 625.0336766499457, (8, 27674): 623.1187025694272, (8, 27688): 624.6335481136238, (8, 27692): 627.0214952123756, (8, 27693): 625.3313038937108, (8, 27705): 625.2704344364682, (8, 27712): 626.1248931496996, (8, 27786): 671.1683122036069, (8, 27790): 663.8870190094821, (8, 27791): 663.2132633857676, (8, 27795): 668.046840993825, (8, 27801): 662.7163205399669, (8, 27813): 673.0153371784046, (8, 27816): 670.7761607520412, (8, 27823): 662.505535509189, (8, 27830): 668.067691990305, (8, 27884): 594.5322682509296, (8, 27885): 608.4279813346426, (8, 27896): 600.016706172248, (8, 27919): 599.4119295728236, (8, 27922): 601.1810191849986, (8, 27930): 596.6132681296364, (8, 27934): 597.1689322488337, (8, 27935): 597.5883530342475, (8, 27948): 665.9994766493771, (8, 27951): 668.8508983086982, (8, 28061): 609.6370093706469, (8, 28290): 729.5733823509851, (8, 28292): 731.6528258658492, (8, 28293): 729.9507555969094, (8, 28295): 728.6965937337493, (8, 28296): 729.3289043987321, (8, 28297): 728.4400734556406, (8, 28302): 727.3748137788348, (8, 28310): 739.8947750643122, (8, 28313): 740.6335338328464, (8, 28372): 743.0468192080874, (8, 28398): 743.0823270050487, (8, 28399): 742.173835749943, (8, 28400): 743.3771498731932, (8, 28401): 740.4788405883514, (8, 28445): 738.8429916035915, (8, 28475): 739.4945028974213, (8, 28885): 143.18920540948773, (8, 28886): 144.78782095922213, (8, 28915): 147.2509679152687, (8, 28916): 146.91315214587374, (8, 28917): 148.03903519495745, (8, 28921): 140.98093651694973, (8, 28931): 142.03734882320518, (8, 28945): 156.84843264236463, (8, 28982): 152.2525553237754, (8, 29219): 166.65071964051552, (8, 29228): 168.72639359084357, (8, 29246): 168.31056877075073, (8, 29248): 172.53056855894786, (8, 29282): 172.72799254149592, (8, 29290): 163.55357633122495, (8, 29291): 164.90107828580645, (8, 29292): 164.2304803333024, (8, 29293): 164.48619119197176, (8, 29294): 166.02723861921953, (8, 29298): 165.54699119700612, (8, 29299): 166.66984394707524, (8, 29304): 164.52687889133432, (8, 29317): 164.04255470588126, (8, 29323): 163.89893016419552, (8, 29330): 164.26440967935534, (8, 29331): 163.57486630771655, (8, 29344): 173.92523868299307, (8, 29445): 215.75362712707212, (8, 29724): 880.4641458296642, (8, 29738): 881.4437588459543, (8, 29745): 878.1790737737452, (8, 29748): 876.6707566955168, (8, 29750): 877.3939463171195, (8, 29759): 875.5834806824415, (8, 29772): 879.1688645827833, (8, 29781): 878.3263274794325, (8, 29784): 878.6025691404213, (8, 29790): 878.7408794799254, (8, 29811): 875.7757213313031, (8, 29817): 876.9168150474655, (8, 29818): 876.0594115589778, (8, 29929): 879.1212418623822, (8, 30039): 897.5141279909705, (8, 30066): 892.451719137994, (8, 30116): 854.8899742131358, (8, 30238): 799.6096019154087, (8, 30248): 832.5171581289122, (8, 30260): 833.6277352717682, (8, 30545): 145.9543484147655, (8, 30733): 185.6602153976351, (8, 30756): 208.00002688540167, (8, 30921): 182.11565957323188, (8, 31079): 299.2188882308739, (8, 31149): 303.0224691138379, (8, 31154): 303.2995078384196, (8, 31160): 303.3653812852431, (8, 31163): 304.1004828165131, (8, 31189): 324.60955719832276, (8, 31215): 323.67399849554977, (8, 31259): 328.0507644939763, (8, 31262): 330.11349368867275, (8, 31430): 299.1452165997123, (8, 31568): 360.8535183889281, (8, 31751): 311.6399141406458, (11, 109): 124.20336942475957, (11, 872): 628.016338790478, (11, 873): 630.5631610103621, (11, 877): 629.8518111945788, (11, 879): 630.2533504608674, (11, 884): 628.2414728040317, (11, 889): 629.7211737022415, (11, 891): 627.3333791129909, (11, 892): 632.1769573424453, (11, 894): 631.7555697265427, (11, 896): 628.8964962124496, (11, 903): 630.2262472241204, (11, 909): 625.0889823574541, (11, 910): 625.8822848255854, (11, 912): 624.2511621439184, (11, 913): 622.5373936226367, (11, 916): 621.480643191633, (11, 926): 626.4201218195665, (11, 927): 625.5144108453335, (11, 948): 626.3710354733013, (11, 961): 626.8584410707416, (11, 962): 626.9895199361127, (11, 963): 627.1878318909174, (11, 967): 631.2037136928799, (11, 974): 630.4075060943064, (11, 998): 632.4119926914128, (11, 1014): 685.14784984414, (11, 1086): 615.1280197956996, (11, 1087): 613.9830779081046, (11, 1089): 612.0691699398058, (11, 1090): 613.2085625323004, (11, 1092): 616.8751820602099, (11, 1097): 614.2412216040211, (11, 1107): 618.1793405491925, (11, 1387): 230.85940616852434, (11, 1554): 196.91068429159358, (11, 1827): 749.0767669578946, (11, 1828): 749.245767061718, (11, 1829): 749.7045910196947, (11, 1830): 749.7758876753616, (11, 1831): 749.9195482684181, (11, 1832): 749.6000138424885, (11, 1833): 749.5493850536037, (11, 1836): 749.1646127018242, (11, 1841): 750.9138662807178, (11, 1843): 750.2310651278644, (11, 1844): 750.6156974653694, (11, 1845): 749.8736385863618, (11, 1847): 747.0033808625944, (11, 1848): 747.9389727281392, (11, 1849): 752.4035937363577, (11, 1850): 752.7877506155352, (11, 1851): 748.8712103402341, (11, 1852): 749.1265676583043, (11, 1854): 749.4262855381393, (11, 1856): 747.1190281577674, (11, 1857): 747.9776339092394, (11, 1858): 751.8476040365316, (11, 1861): 749.8074772461771, (11, 1866): 747.2217829621286, (11, 1867): 750.8026416645863, (11, 1868): 750.1008764200076, (11, 1870): 750.7820348260198, (11, 1871): 750.5207157919886, (11, 1875): 749.2523764723809, (11, 1880): 747.5338569449767, (11, 1882): 748.0765699926319, (11, 1883): 752.6104102698603, (11, 1889): 747.7035281678483, (11, 1893): 749.4473105256336, (11, 1894): 748.747207626483, (11, 1899): 747.0045689024784, (11, 1900): 747.4166172288062, (11, 1902): 750.5687874983352, (11, 1905): 751.5255056775127, (11, 1907): 748.3719557756108, (11, 1910): 748.4468859285154, (11, 1917): 752.6655461377724, (11, 1920): 748.2686200032185, (11, 1935): 751.2775304987044, (11, 1937): 752.0495830814427, (11, 1946): 745.1419991619891, (11, 1949): 745.8338382445144, (11, 1950): 743.5437646764195, (11, 1951): 744.7531924725309, (11, 1952): 746.2412510062618, (11, 1953): 746.2228327176305, (11, 1954): 745.925618400387, (11, 1958): 745.8146057761073, (11, 1960): 747.273476814161, (11, 1968): 747.8479970752229, (11, 1969): 751.0731062876122, (11, 1974): 750.2628614485673, (11, 1975): 750.3761089646176, (11, 1979): 748.2502167539907, (11, 1980): 748.4735389649129, (11, 1981): 748.7898425102231, (11, 1985): 749.1394048545392, (11, 1994): 743.3278361511595, (11, 2011): 748.1692322654466, (11, 2019): 755.2788366301145, (11, 2020): 754.3417096143471, (11, 2029): 751.142927352813, (11, 2030): 753.6863291105709, (11, 2032): 750.8059840993352, (11, 2033): 752.3232616238893, (11, 2034): 752.4751959597198, (11, 2036): 749.9687916559191, (11, 2037): 750.5812523510369, (11, 2038): 750.0095069610375, (11, 2042): 760.2318564690007, (11, 2050): 751.5981573740645, (11, 2051): 751.6469941459544, (11, 2053): 751.8321283713144, (11, 2054): 752.7433048997462, (11, 2066): 750.923596297389, (11, 2067): 750.8289118991545, (11, 2071): 741.5261549797748, (11, 2072): 743.0629633227715, (11, 2073): 737.9361519033425, (11, 2074): 737.8345153719682, (11, 2080): 735.3134348237581, (11, 2082): 743.9361068156643, (11, 2083): 744.7188549014232, (11, 2089): 742.7408383358903, (11, 2090): 743.4372415369288, (11, 2092): 742.2259106620965, (11, 2098): 736.142098994906, (11, 2099): 737.23447798984, (11, 2101): 736.1411247390062, (11, 2102): 740.4718226289009, (11, 2103): 739.1814955263272, (11, 2104): 738.5588433367645, (11, 2106): 745.3796609713492, (11, 2112): 736.8807265944147, (11, 2113): 741.1965562025574, (11, 2114): 742.5449343118336, (11, 2117): 746.1859867922155, (11, 2123): 732.7062848024458, (11, 2124): 733.598695437557, (11, 2134): 731.5397696918787, (11, 2138): 733.9720879627525, (11, 2141): 731.7002019194927, (11, 2148): 734.8766082999524, (11, 2150): 729.6179359421318, (11, 2151): 730.6948724048079, (11, 2152): 729.2522926391924, (11, 2153): 735.0000745712758, (11, 2154): 731.1843716798757, (11, 2155): 731.0742346189262, (11, 2156): 730.1601453954296, (11, 2157): 732.2487362837458, (11, 2160): 736.1226549368896, (11, 2161): 729.2844973307022, (11, 2162): 735.8627967055835, (11, 2163): 734.5458724791104, (11, 2164): 734.5751524803541, (11, 2168): 730.9404909693983, (11, 2172): 732.6317346793948, (11, 2174): 730.8229298771067, (11, 2178): 733.6155560526023, (11, 2179): 733.1087137334172, (11, 2183): 734.1282441505575, (11, 2185): 734.3004677793896, (11, 2186): 733.5264455142857, (11, 2190): 736.092843620547, (11, 2192): 734.7392509186923, (11, 2193): 734.3136045848731, (11, 2194): 732.9316987738762, (11, 2195): 732.9807748074774, (11, 2197): 735.1572158040723, (11, 2205): 733.5749042092834, (11, 2207): 731.4377096206631, (11, 2208): 732.6825614091741, (11, 2212): 734.1711901779743, (11, 2214): 710.7574726911057, (11, 2225): 714.699803435239, (11, 2231): 703.0237652597648, (11, 2278): 729.7673674204226, (11, 2284): 732.9563566696085, (11, 2285): 732.7257923388107, (11, 2291): 728.2411857109754, (11, 2292): 727.5638077338406, (11, 2307): 731.171160064142, (11, 2313): 727.9839897885478, (11, 2317): 724.9783926956688, (11, 2319): 728.6525576234558, (11, 2321): 730.1488926961928, (11, 2323): 729.618808863128, (11, 2326): 733.8427964988635, (11, 2327): 732.6290252802218, (11, 2329): 731.8378206418228, (11, 2330): 731.0216467343607, (11, 2332): 733.1903721298106, (11, 2344): 729.576089255775, (11, 2346): 729.7716108713952, (11, 2361): 727.1879445312237, (11, 2368): 742.5667412844887, (11, 2374): 744.0983034349695, (11, 2375): 744.420285793955, (11, 2377): 739.5592697545297, (11, 2378): 745.3716369178799, (11, 2379): 745.7421405100271, (11, 2380): 746.0255932703209, (11, 2383): 740.6542671989636, (11, 2385): 741.2890688136628, (11, 2395): 741.1449264357326, (11, 2397): 745.2989415458842, (11, 2398): 738.038521229415, (11, 2399): 739.6108071909256, (11, 2400): 739.2266832796728, (11, 2402): 742.6149154506626, (11, 2403): 743.6828201293082, (11, 2404): 743.8548358031309, (11, 2405): 741.3739594911384, (11, 2407): 743.2454796205549, (11, 2408): 744.6055396451048, (11, 2409): 742.0871481380092, (11, 2411): 744.0927086952995, (11, 2412): 743.6560043587107, (11, 2413): 744.5892431247372, (11, 2414): 743.221984620122, (11, 2422): 743.9131694442195, (11, 2424): 743.8657723843149, (11, 2426): 744.0120785141795, (11, 2433): 742.1889074880017, (11, 2436): 741.9340244648348, (11, 2437): 735.6397584829343, (11, 2440): 736.9523870737409, (11, 2445): 766.6462585098075, (11, 2447): 763.0411080887642, (11, 2454): 766.2095464126323, (11, 2455): 766.1909996857033, (11, 2460): 756.6117975029464, (11, 2461): 757.8367704080194, (11, 2471): 778.5148967959454, (11, 2492): 765.134201220861, (11, 2511): 754.1601995756529, (11, 2523): 759.800755405188, (11, 2525): 758.7215331709443, (11, 2535): 757.4124339931906, (11, 2537): 755.3771673539057, (11, 2538): 756.5960106419294, (11, 2539): 756.881814441373, (11, 2540): 758.3591130569508, (11, 2542): 760.1523461263655, (11, 2559): 788.5620075809734, (11, 2575): 786.9089719343431, (11, 2599): 738.4565515384977, (11, 2600): 749.3478953004624, (11, 2607): 742.341740441487, (11, 2627): 763.3218186719987, (11, 2647): 769.6017852026084, (11, 2674): 765.7278460599305, (11, 2681): 765.4023112502091, (11, 2683): 767.9653354871833, (11, 2686): 764.5571142317276, (11, 2689): 801.9631824540601, (11, 2690): 802.254101817648, (11, 2713): 812.7131320364108, (11, 2714): 813.78305392171, (11, 2715): 814.6699599268214, (11, 2739): 813.7512433494379, (11, 2740): 806.9017003995303, (11, 2741): 807.2542350203497, (11, 2749): 812.9971551263739, (11, 2750): 813.1160432690111, (11, 2752): 813.6768818467345, (11, 2755): 814.4795467203185, (11, 2758): 814.408115519815, (11, 2759): 814.3397817576234, (11, 2769): 813.1265398081835, (11, 2771): 808.6631005673547, (11, 2779): 810.102793980547, (11, 2784): 800.5706143457766, (11, 2800): 803.5062412334282, (11, 2802): 805.7997451877704, (11, 2803): 805.3144758928674, (11, 2804): 804.6605295433194, (11, 2805): 806.9916341718099, (11, 2807): 806.788265048471, (11, 2809): 806.7855691625932, (11, 2812): 800.6830239844164, (11, 2814): 807.4579836785371, (11, 2817): 808.963698338729, (11, 2819): 806.5428704548061, (11, 2823): 802.5131547219393, (11, 2832): 808.3097188213633, (11, 2836): 804.2668824078652, (11, 2839): 806.6255378898508, (11, 2841): 808.5001702637106, (11, 2843): 807.9660654535008, (11, 2846): 805.6585719752999, (11, 2849): 809.1887932385787, (11, 2852): 808.1766313182128, (11, 2853): 809.6637130405815, (11, 2876): 810.7561779092674, (11, 2877): 814.0992789933908, (11, 2885): 816.4630103705852, (11, 2918): 806.0519946712387, (11, 2921): 807.6270542060728, (11, 2925): 799.7472491657317, (11, 2926): 796.8334151258626, (11, 2930): 804.1710473095109, (11, 2931): 800.765552591136, (11, 2938): 806.3288299024676, (11, 2940): 809.1688622310479, (11, 2947): 804.0598914988194, (11, 2949): 803.5430267012187, (11, 2950): 804.4275564386481, (11, 2952): 803.7438112507689, (11, 2958): 803.5039095753998, (11, 2959): 803.8743892876417, (11, 2960): 805.513425251693, (11, 2961): 804.8910963384773, (11, 2963): 803.0662581536078, (11, 2968): 803.6579133057359, (11, 2976): 802.7272716862363, (11, 2981): 791.4500394417962, (11, 2982): 791.3771837092768, (11, 2984): 790.7678792994343, (11, 3003): 789.9107775733048, (11, 3046): 777.524241962013, (11, 3050): 786.1773823828713, (11, 3051): 786.5981064765691, (11, 3053): 785.2278641670192, (11, 3069): 794.1104421519714, (11, 3071): 784.1654572818511, (11, 3080): 816.9809020850017, (11, 3199): 789.5465916749981, (11, 3200): 788.1788610053139, (11, 3205): 797.6945187382321, (11, 3209): 789.0343165960929, (11, 3215): 788.108424165765, (11, 3217): 786.219898011049, (11, 3249): 788.1037502311063, (11, 3263): 802.2911643896148, (11, 3289): 792.1328254124498, (11, 3301): 793.0240085222555, (11, 3302): 792.1823220467014, (11, 3307): 791.28787619171, (11, 3310): 793.8375498308836, (11, 3391): 803.8081115018259, (11, 3509): 477.8127752414898, (11, 3510): 476.4480262158467, (11, 3511): 477.10004690664243, (11, 3512): 476.0306171399409, (11, 3514): 476.11373434370284, (11, 3519): 482.26709969329215, (11, 3536): 479.76912195150646, (11, 3545): 481.65254898158673, (11, 3548): 479.22328307792543, (11, 3572): 480.8557305324084, (11, 3581): 480.056968412239, (11, 3583): 478.0721498841399, (11, 3601): 485.2257100579009, (11, 3656): 483.990923348686, (11, 3669): 483.4435093567779, (11, 3670): 484.7555247448656, (11, 3695): 476.885669269684, (11, 3696): 477.813840537113, (11, 3782): 475.2599082852353, (11, 3792): 474.4384317536641, (11, 3989): 218.83618740861738, (11, 4008): 225.87098471672147, (11, 4031): 228.8464046914367, (11, 4045): 223.07333386022867, (11, 4144): 220.2350038269772, (11, 4145): 209.62981477183217, (11, 4164): 216.67842685895113, (11, 4168): 212.83342224974402, (11, 4173): 211.56383655944498, (11, 4181): 207.27881589912008, (11, 4228): 207.02744449635534, (11, 4248): 200.1736409817685, (11, 4254): 146.06329752722522, (11, 4260): 148.03391161418804, (11, 4262): 149.24645096153696, (11, 4273): 149.891869796004, (11, 4319): 117.53048043694625, (11, 4326): 117.23923419478274, (11, 4328): 118.07783406982028, (11, 4334): 117.9434994894802, (11, 4335): 117.03514361915, (11, 4372): 124.17834242946634, (11, 4413): 144.44621415350613, (11, 4434): 122.06134984803424, (11, 4447): 119.24072906323633, (11, 4452): 122.99378247456083, (11, 4463): 135.6963939873709, (11, 4465): 134.05817167550606, (11, 4619): 160.26395368050538, (11, 4645): 160.20104592670432, (11, 4657): 161.60352893669008, (11, 4666): 162.35229393968078, (11, 4676): 163.78255893439396, (11, 4678): 163.28899398322133, (11, 4689): 164.36649827720964, (11, 4704): 172.49381654099955, (11, 4726): 229.1904891295995, (11, 4727): 228.286271237508, (11, 4730): 226.43046752456232, (11, 4731): 227.64187678699108, (11, 4734): 224.76443841846768, (11, 4735): 224.48586088078096, (11, 4736): 225.4230872101453, (11, 4737): 224.5892402892087, (11, 4738): 225.20132355482417, (11, 4756): 226.4160723165629, (11, 4760): 219.02880331683394, (11, 4761): 218.4000571819411, (11, 4762): 218.4874108758651, (11, 4765): 219.81596144190337, (11, 4773): 230.4076311659545, (11, 4774): 230.52446566848707, (11, 4790): 229.6682745128505, (11, 4795): 228.6470686549987, (11, 4799): 231.40474924196107, (11, 4801): 234.5606561554889, (11, 4804): 227.801841051883, (11, 4805): 226.97597006481132, (11, 4806): 231.54733315583644, (11, 4815): 231.50103711852518, (11, 4816): 233.33586953574257, (11, 4817): 234.84964618612779, (11, 4826): 233.17762138241258, (11, 4830): 232.35612967938795, (11, 4839): 221.71650787349185, (11, 4840): 222.98092593886892, (11, 4841): 221.44875009995116, (11, 4846): 220.6419045503898, (11, 4848): 221.36211182376613, (11, 4850): 222.3394880090209, (11, 4871): 207.6299939375919, (11, 4883): 216.6668897770476, (11, 4900): 210.71877031578592, (11, 4901): 210.3328443303484, (11, 4917): 180.59909272396493, (11, 4931): 176.08469717836263, (11, 4944): 180.331649123559, (11, 4956): 177.69780925878752, (11, 4958): 179.14078321756247, (11, 4959): 179.37957635935746, (11, 4961): 177.9650423603749, (11, 4966): 177.5226666946246, (11, 5207): 172.85681383255454, (11, 5272): 74.5201391451972, (11, 5283): 74.34321041460757, (11, 5287): 77.95910260237378, (11, 5289): 78.1485820030489, (11, 5293): 71.12386490396123, (11, 5295): 70.13417040868403, (11, 5296): 72.365519832615, (11, 5298): 73.62462826764136, (11, 5303): 75.49086072291665, (11, 5305): 78.86256331823776, (11, 5306): 82.1652732592441, (11, 5307): 79.22545867359568, (11, 5308): 79.42766192586095, (11, 5313): 76.71718881230679, (11, 5314): 75.6978912486822, (11, 5317): 80.85471782129817, (11, 5319): 76.12711388922689, (11, 5324): 74.49285709003271, (11, 5326): 73.35634143042364, (11, 5348): 84.09813534144516, (11, 5351): 87.00589637392437, (11, 5399): 81.55090519605076, (11, 5413): 91.92672586273736, (11, 5422): 79.22859570828028, (11, 5445): 80.37216601063501, (11, 5448): 80.56691898619589, (11, 5456): 82.99945997084654, (11, 5467): 83.4865549104201, (11, 5624): 82.83229056548375, (11, 5671): 50.146192969575274, (11, 5672): 48.234527356221506, (11, 5797): 78.89892802816253, (11, 5871): 112.23930939556622, (11, 5976): 106.1060560422221, (11, 6118): 661.1999165178361, (11, 6248): 696.602045383251, (11, 6345): 217.03137224771277, (11, 6352): 223.50773018019166, (11, 6354): 214.9101819727792, (11, 6359): 214.6002920001661, (11, 6376): 224.82215967108968, (11, 6378): 215.78708787731736, (11, 6381): 215.80274170475224, (11, 6383): 218.01934139327082, (11, 6396): 220.4065926432255, (11, 6399): 218.11447355341943, (11, 6408): 222.3219033355523, (11, 6409): 216.7612738942331, (11, 6419): 223.48345467391349, (11, 6422): 219.50115990114568, (11, 6423): 219.88787162427488, (11, 6424): 212.6965928219559, (11, 6439): 213.13123222922343, (11, 6464): 214.15130978763628, (11, 6465): 215.6571809200086, (11, 6469): 216.66821924741092, (11, 6470): 217.4874525111313, (11, 6472): 212.79785227910148, (11, 6480): 209.87874287098867, (11, 6486): 201.55394838213746, (11, 6497): 204.12890741848935, (11, 6503): 208.72936509808767, (11, 6508): 210.96045602018054, (11, 6509): 208.46664911068027, (11, 6521): 207.1737147451942, (11, 6544): 204.98344386334847, (11, 6552): 213.95941358454476, (11, 6553): 214.7036416473331, (11, 6554): 215.49714683187628, (11, 6578): 213.09832154851645, (11, 6582): 211.0114901794155, (11, 6601): 212.17897754149257, (11, 6609): 208.58140543674915, (11, 6610): 207.7562985527448, (11, 6611): 209.13690356753213, (11, 6614): 210.4831775112776, (11, 6615): 209.79409530665706, (11, 6616): 206.93736895379672, (11, 6617): 208.01714708755273, (11, 6618): 204.7792720851758, (11, 6619): 210.76458500172637, (11, 6620): 205.9629042875817, (11, 6621): 206.47085729847956, (11, 6622): 206.96689384661883, (11, 6623): 209.51062567839014, (11, 6624): 209.1333851072406, (11, 6625): 209.77939547475606, (11, 6626): 211.22242847869302, (11, 6627): 211.49527791291416, (11, 6628): 205.13721850763926, (11, 6629): 207.7689562053972, (11, 6630): 211.91303290745174, (11, 6632): 208.36938756464787, (11, 6634): 212.0585690066164, (11, 6635): 207.23871129939073, (11, 6636): 206.56621451319398, (11, 6637): 208.63290737535027, (11, 6638): 210.91810713916092, (11, 6639): 210.86167082641558, (11, 6640): 211.28329811270888, (11, 6641): 205.74406020377094, (11, 6642): 210.26689430140968, (11, 6643): 211.98540054466153, (11, 6645): 210.23124816953984, (11, 6646): 205.78608501709348, (11, 6647): 210.40787674733176, (11, 6653): 210.12163809079055, (11, 6655): 211.16632514425342, (11, 6658): 211.7388370039816, (11, 6662): 209.6270037354318, (11, 6819): 240.66449945790453, (11, 6996): 214.08544211635152, (11, 7059): 204.0342084501975, (11, 7187): 200.77150542787712, (11, 7304): 234.73867505504583, (11, 7528): 204.86166335223797, (11, 7720): 155.12810546545433, (11, 7793): 151.08836845089004, (11, 7807): 151.99172185510625, (11, 7808): 150.20384668779184, (11, 7831): 196.9200853174405, (11, 7850): 193.3603015592518, (11, 7852): 196.6488672814323, (11, 8012): 165.1686861919625, (11, 8125): 123.98684027992786, (11, 8208): 138.05700728426018, (11, 8392): 175.51504572967443, (11, 8651): 289.1424059551398, (11, 9088): 259.6996613401678, (11, 9443): 288.104115295863, (11, 9444): 286.21116585902166, (11, 9828): 331.7885827012987, (11, 9868): 338.96712793167205, (11, 10180): 121.22632244864097, (11, 10256): 92.74141876022311, (11, 10276): 109.15185470378567, (11, 10378): 118.89316185556605, (11, 10676): 119.79844631782058, (11, 10714): 137.68745379695, (11, 10730): 139.54309323365783, (11, 10862): 231.16479021935885, (11, 10881): 229.53801749250496, (11, 10883): 230.39257263810757, (11, 10885): 231.35523208339507, (11, 10891): 231.73634753364212, (11, 10909): 230.26549696449322, (11, 10911): 228.38448717407803, (11, 10913): 229.2936828050876, (11, 10915): 228.45980699676724, (11, 10919): 227.5170243754667, (11, 11037): 259.25464104045926, (11, 11039): 257.46868339286215, (11, 11516): 325.1367359379943, (11, 11856): 118.31696107835242, (11, 11857): 114.876554969364, (11, 11861): 116.55769401028931, (11, 11881): 119.50085538121981, (11, 11902): 116.88445021624173, (11, 11911): 119.28300991909695, (11, 11914): 118.38153872898819, (11, 11922): 119.30914490559474, (11, 11924): 120.65537916574908, (11, 11926): 120.06095734045032, (11, 11950): 124.64396567973247, (11, 11963): 126.77404950990912, (11, 11983): 130.07785949731363, (11, 11985): 127.64897709089459, (11, 12009): 131.32825909869354, (11, 12010): 128.7557244535965, (11, 12018): 129.57632492463912, (11, 12020): 129.38973641472825, (11, 12021): 130.11006637677073, (11, 12024): 131.6463104850773, (11, 12025): 130.27171875117685, (11, 12027): 130.1154206979665, (11, 12031): 128.47511018091714, (11, 12032): 128.32146435004864, (11, 12035): 132.19012964962687, (11, 12041): 125.43914635902284, (11, 12045): 114.3395276022245, (11, 12145): 124.34090024820684, (11, 12275): 228.9938129498128, (11, 12294): 228.5109353075679, (11, 12358): 248.55687426384375, (11, 12463): 259.455394263603, (11, 12465): 259.51362392297443, (11, 12482): 258.6346513541203, (11, 12503): 259.168396106093, (11, 12506): 259.864055183454, (11, 12549): 253.9212632584283, (11, 12559): 254.27622071389797, (11, 12569): 256.420202299944, (11, 12572): 256.851794212593, (11, 12574): 255.46139679138082, (11, 12576): 253.99468221047908, (11, 12591): 251.33169328473628, (11, 12608): 253.77869166849436, (11, 12696): 245.27913077250705, (11, 12710): 245.92821290618747, (11, 12728): 247.53776099698572, (11, 12766): 192.9620260057788, (11, 12771): 183.09545295059903, (11, 12790): 183.70504058767574, (11, 12795): 186.50824760659285, (11, 12797): 182.03494868668824, (11, 12798): 181.27508748955697, (11, 12811): 180.25030171844622, (11, 12830): 182.60858671325576, (11, 12848): 178.24384726149748, (11, 12850): 175.62960543895932, (11, 12852): 181.40404791065458, (11, 12854): 181.59685901051378, (11, 12859): 176.9644353183359, (11, 12861): 180.09414925197504, (11, 12865): 181.92382385300297, (11, 12866): 180.75532973130862, (11, 12867): 181.60186879392495, (11, 12874): 181.35784962462859, (11, 12875): 180.7234978901402, (11, 12881): 182.6019844464598, (11, 12883): 182.26515265713115, (11, 12885): 180.9257237981736, (11, 12888): 181.53555106183387, (11, 12889): 180.77148961859885, (11, 12892): 181.8075717512793, (11, 12893): 182.37997661193955, (11, 12896): 181.4214189094004, (11, 12906): 185.14646196659336, (11, 13018): 208.9062854525038, (11, 13071): 213.73713648441637, (11, 13131): 197.0722195587755, (11, 13146): 190.77345553130925, (11, 13159): 218.6072707523285, (11, 13193): 196.18567475796047, (11, 13198): 194.02624372063244, (11, 13292): 185.2453646937653, (11, 13296): 175.16483558391516, (11, 13406): 210.7212811182716, (11, 13407): 211.9410581741059, (11, 13417): 220.3401455506894, (11, 13418): 220.90671872419966, (11, 13438): 211.78594600521583, (11, 13442): 208.54706221847835, (11, 13443): 209.4415342290138, (11, 13764): 331.133320268374, (11, 13766): 329.777644173415, (11, 13771): 333.5013870957584, (11, 13783): 328.2909222131525, (11, 13784): 327.2638280304343, (11, 13792): 339.72006859913364, (11, 13824): 329.7078902493561, (11, 14017): 307.84559881590786, (11, 14870): 197.73846901955957, (11, 14997): 207.68899701067062, (11, 15000): 206.7690568861889, (11, 15003): 204.83897091597586, (11, 15006): 205.5370191059423, (11, 15007): 204.26155597878014, (11, 15056): 202.0918543248251, (11, 15063): 202.724029539117, (11, 15069): 202.28338326641503, (11, 15076): 203.51334926422135, (11, 15086): 208.27328618379252, (11, 15087): 208.47269231628312, (11, 15111): 212.84260401741903, (11, 15116): 210.2549831245698, (11, 15722): 242.783197910159, (11, 15998): 250.81087446080542, (11, 16073): 573.1166832083218, (11, 16939): 676.8089534859275, (11, 16940): 674.9077838264096, (11, 16951): 677.7378921467331, (11, 16963): 677.7561867285951, (11, 16965): 679.77670670218, (11, 16969): 679.6334188232382, (11, 16970): 678.3582329690695, (11, 16971): 676.513432018416, (11, 16973): 676.6296987530585, (11, 16974): 680.8188473739394, (11, 16976): 678.3492788386349, (11, 16978): 676.9172817713135, (11, 16980): 678.8267436453259, (11, 16982): 681.0546314587983, (11, 17045): 757.9488649234173, (11, 17048): 760.4836748872568, (11, 17304): 185.84002761154494, (11, 17305): 187.39045006463564, (11, 17330): 187.49710508115842, (11, 17334): 183.57077157188698, (11, 17343): 189.36301401178713, (11, 17345): 186.1191028529127, (11, 17347): 189.06850097007805, (11, 17351): 181.1141642808831, (11, 17372): 184.35675289787338, (11, 17373): 188.86029505057016, (11, 17377): 189.3892054792037, (11, 17382): 187.00506303331053, (11, 17383): 186.57538468205578, (11, 17389): 185.38230215581572, (11, 17400): 187.38158673306006, (11, 17401): 186.92303660703706, (11, 17402): 187.7728842270033, (11, 17403): 188.2212654653613, (11, 17440): 189.10355784958446, (11, 17455): 190.65723273097302, (11, 17491): 192.80462410013362, (11, 17507): 176.12707324060494, (11, 17509): 176.7126295606042, (11, 17590): 183.2524820415049, (11, 17615): 159.56857016157753, (11, 17642): 162.1164216508549, (11, 17643): 163.0228148642752, (11, 17668): 158.883694338056, (11, 17721): 150.28920515253924, (11, 17754): 160.5934415142465, (11, 17769): 173.59490358475594, (11, 17776): 173.49807123828728, (11, 17804): 175.15831094182752, (11, 17809): 176.40367663931207, (11, 17824): 173.98233601958404, (11, 17837): 178.05206441941183, (11, 17838): 179.65717079278838, (11, 17862): 179.47719883670487, (11, 17866): 181.32257793400973, (11, 17872): 177.7251991175256, (11, 17873): 176.6845139202712, (11, 17881): 178.51379157239293, (11, 17947): 515.7044430653883, (11, 17951): 512.7750912152746, (11, 17953): 511.9297218991806, (11, 17954): 511.9475360049635, (11, 17959): 515.5927775060851, (11, 17963): 515.0575193443311, (11, 18000): 499.3785592202813, (11, 18001): 499.5801128610561, (11, 18111): 531.0180992610451, (11, 18148): 449.4834097150741, (11, 18166): 479.3879485034046, (11, 18189): 510.5444557906975, (11, 18239): 188.5007345032944, (11, 18240): 188.76988798273376, (11, 18245): 188.761752436569, (11, 18247): 188.79680287058076, (11, 18251): 189.1024218112038, (11, 18256): 189.76436391781013, (11, 18258): 189.62202486669446, (11, 18259): 189.83014899938505, (11, 18260): 190.162926177554, (11, 18262): 190.58633737812352, (11, 18263): 190.00634557852007, (11, 18264): 190.31910657898047, (11, 18266): 190.9298865501215, (11, 18267): 191.19586515512776, (11, 18268): 191.43270592638729, (11, 18269): 191.9929538257729, (11, 18275): 191.7299261383742, (11, 18285): 190.10085370936042, (11, 18308): 184.21956776217016, (11, 18313): 183.02624510902916, (11, 18314): 184.45895541245406, (11, 18315): 191.17968692199213, (11, 18316): 191.52258921062807, (11, 18317): 191.80857662181714, (11, 18320): 191.52776115939875, (11, 18321): 191.8563303030997, (11, 18322): 192.22966619936335, (11, 18324): 191.99266701729653, (11, 18325): 192.62756835566796, (11, 18326): 192.37350984217775, (11, 18327): 192.38818935706442, (11, 18329): 192.49059724192156, (11, 18330): 193.3506153928661, (11, 18331): 192.73983813156073, (11, 18332): 192.30674020748066, (11, 18333): 192.9474951310452, (11, 18336): 192.02465766226567, (11, 18337): 191.99872873152427, (11, 18403): 193.8088914227623, (11, 18432): 196.57149546238418, (11, 18451): 194.69398446286084, (11, 18466): 192.09538702124033, (11, 18481): 190.33896798639265, (11, 18483): 190.60716216430052, (11, 18484): 190.05168793038982, (11, 18485): 188.10508236530384, (11, 18486): 188.08300741786152, (11, 18487): 186.93980413303197, (11, 18489): 188.89874800870214, (11, 18490): 188.98207510269066, (11, 18491): 189.36617399912978, (11, 18492): 186.34773579340447, (11, 18493): 187.62460055793036, (11, 18494): 188.9615983859318, (11, 18495): 188.65561514351586, (11, 18496): 188.47479385674674, (11, 18497): 186.42626992529776, (11, 18498): 187.7146904216628, (11, 18499): 188.41291769132326, (11, 18501): 187.42957922293382, (11, 18502): 186.95143076963848, (11, 18503): 186.9146821099108, (11, 18504): 188.96629490378493, (11, 18506): 186.7187767267059, (11, 18507): 186.10815716808165, (11, 18508): 188.0533711433609, (11, 18509): 187.80582041676658, (11, 18510): 186.54717025870497, (11, 18511): 187.20806268464045, (11, 18512): 187.19531136450385, (11, 18515): 188.62496809389202, (11, 18516): 187.77228081195972, (11, 18517): 186.78044897989147, (11, 18518): 188.3762174678367, (11, 18519): 189.21778966102895, (11, 18520): 188.24532137590728, (11, 18522): 191.6053784400061, (11, 18523): 191.40118092844173, (11, 18532): 191.56656754111006, (11, 18535): 190.92234088634993, (11, 18537): 190.56562170959828, (11, 18539): 190.48606234674756, (11, 18540): 190.36475906564075, (11, 18541): 190.40622269808614, (11, 18542): 190.46089555544688, (11, 18543): 190.07064397277637, (11, 18546): 189.75475365057773, (11, 18555): 190.29044974687636, (11, 18556): 190.18811059612648, (11, 18565): 191.12909244383607, (11, 18567): 190.71039512728208, (11, 18568): 190.66269113909075, (11, 18577): 192.92305811908224, (11, 18583): 193.3421483036801, (11, 18605): 194.7832999228438, (11, 18608): 189.72943697965496, (11, 18616): 196.86885582118367, (11, 18618): 198.17887400412837, (11, 18625): 199.65346769635718, (11, 18645): 198.92367859742322, (11, 18646): 198.63997144576032, (11, 18653): 195.11064378863045, (11, 18654): 196.4776095468923, (11, 18655): 195.14105703313132, (11, 18666): 204.64941338614534, (11, 18837): 229.7640877715083, (11, 18974): 201.6115498146895, (11, 18999): 206.7098638174169, (11, 19000): 207.2917127774337, (11, 19174): 205.39942464899744, (11, 19342): 220.6803547092487, (11, 19455): 192.4016435785337, (11, 19555): 188.0973839772674, (11, 19564): 198.90883918078467, (11, 19573): 196.25273640037872, (11, 19586): 194.41233511361568, (11, 19605): 192.96663468678892, (11, 19611): 194.3750370879666, (11, 19614): 190.9638507042698, (11, 19641): 203.3226977244286, (11, 19702): 206.20594015312528, (11, 19713): 204.5878095325923, (11, 19731): 171.2962572742119, (11, 19819): 195.40487231173947, (11, 19893): 26.16656745229178, (11, 19899): 24.0, (11, 19929): 26.840318556326448, (11, 19951): 33.686329831883555, (11, 19962): 24.0, (11, 19970): 31.088763688292403, (11, 19971): 29.171991073449718, (11, 19972): 27.591499788233826, (11, 19975): 28.945304776864404, (11, 19978): 41.90667290876399, (11, 19987): 42.990151216028494, (11, 19989): 39.908597137064504, (11, 20039): 44.058366084845595, (11, 20043): 46.73962802559097, (11, 20047): 46.722083648691736, (11, 20052): 42.399867071628236, (11, 20054): 41.94899561798975, (11, 20085): 68.30544694927804, (11, 20104): 69.9092001358181, (11, 20132): 59.3298573089521, (11, 20203): 24.0, (11, 20280): 24.0, (11, 20285): 24.0, (11, 20290): 24.0, (11, 20297): 24.0, (11, 20309): 36.59360462980196, (11, 20453): 68.73822179231814, (11, 20485): 24.0, (11, 20520): 24.0, (11, 20526): 24.0, (11, 20698): 408.51582052706567, (11, 20868): 462.68894779176225, (11, 21042): 126.41127512233948, (11, 21057): 124.25774345801489, (11, 21066): 122.54803755726289, (11, 21075): 126.70858552279978, (11, 21093): 122.67798207483189, (11, 21098): 115.58693128206926, (11, 21127): 124.3014539259589, (11, 21130): 122.03267905113351, (11, 21144): 125.46345845417494, (11, 21146): 124.51433456593553, (11, 21147): 126.5145647907413, (11, 21148): 124.88432094380279, (11, 21153): 139.09594594438394, (11, 21293): 118.48261443775884, (11, 21426): 152.96757082015426, (11, 21442): 159.88502603274074, (11, 21451): 160.47063749872794, (11, 21466): 154.3854054090763, (11, 21469): 153.72454139884823, (11, 21471): 154.8044339031565, (11, 21473): 153.82685067705143, (11, 21475): 154.237578078148, (11, 21482): 154.72146207693226, (11, 21484): 154.1145505516254, (11, 21488): 154.87269634214746, (11, 21494): 152.3048690155193, (11, 21498): 152.2920741520209, (11, 21500): 150.79260007635156, (11, 21514): 143.06431125690258, (11, 21537): 146.54744693649636, (11, 21662): 137.73150979466595, (11, 21691): 138.8967443079771, (11, 21757): 156.12402878871313, (11, 21777): 125.39471419126215, (11, 21778): 126.62482933106966, (11, 21779): 124.55455293606855, (11, 21790): 125.57108404563857, (11, 21802): 122.86744009309318, (11, 21824): 120.2178559273124, (11, 21874): 122.54900805701874, (11, 21879): 120.83669046681024, (11, 21983): 130.2857086444298, (11, 22002): 109.38742622573214, (11, 22132): 152.84591618194312, (11, 22261): 336.72085790979384, (11, 22298): 331.8137833566543, (11, 22339): 353.2280247666705, (11, 22508): 298.1033095818793, (11, 22841): 812.1015771815207, (11, 22842): 812.0126515164014, (11, 22874): 806.7700301829042, (11, 22941): 807.610499057801, (11, 22956): 810.5191691676387, (11, 22960): 811.6395456842549, (11, 22968): 813.208944302397, (11, 22970): 814.2339214931862, (11, 22974): 814.8078597944472, (11, 22980): 818.3922256946313, (11, 23025): 816.6813631365873, (11, 23028): 815.5952720983008, (11, 23081): 819.8625724247556, (11, 23104): 810.8601949255892, (11, 23147): 783.3575161531188, (11, 23298): 133.25343692938577, (11, 23376): 131.77080097917045, (11, 23381): 122.24925542449539, (11, 23529): 127.15320552965221, (11, 23556): 127.29999804179721, (11, 23718): 139.57929449919166, (11, 24001): 148.45821886774738, (11, 24094): 139.97763414600195, (11, 24129): 143.33728124197538, (11, 24174): 130.92040302753222, (11, 24235): 134.70957127540703, (11, 24259): 141.72491182198854, (11, 24260): 140.92248491461694, (11, 24261): 140.65570162775668, (11, 24305): 147.44587981100454, (11, 24306): 147.47443495465035, (11, 24307): 146.77830630968398, (11, 24308): 165.27980740337324, (11, 24498): 167.59247220518418, (11, 24499): 167.4338148174236, (11, 24500): 166.97142088666212, (11, 24668): 175.51356589608397, (11, 24711): 167.08023567424522, (11, 24756): 165.50164749255376, (11, 24788): 168.51975493346512, (11, 24809): 159.53847663907152, (11, 24813): 162.7049485035649, (11, 24821): 161.83115082444624, (11, 24825): 161.76112485123238, (11, 24832): 159.50562743780154, (11, 24833): 160.46045509702273, (11, 24835): 161.1960960806017, (11, 24837): 163.22976853933258, (11, 24840): 159.0948808312269, (11, 24841): 161.11439497362068, (11, 24844): 158.78232398098413, (11, 24845): 161.04211395276522, (11, 24846): 159.00543829588653, (11, 24849): 159.3579164569641, (11, 24850): 162.56484964571138, (11, 24863): 152.07246550491308, (11, 24866): 153.86433375344217, (11, 24885): 154.62316292259231, (11, 24886): 153.98041542005902, (11, 24889): 160.4904960079422, (11, 24903): 163.15391718418098, (11, 24909): 158.96774096560668, (11, 24999): 242.9891193168855, (11, 25019): 243.4896656039935, (11, 25028): 241.33866836703032, (11, 25137): 27.12287559858197, (11, 25145): 27.099964865016613, (11, 25208): 55.245033578062426, (11, 25233): 54.6353196203376, (11, 25371): 24.0, (11, 25377): 24.0, (11, 25828): 117.29267457427734, (11, 25851): 134.4889645162492, (11, 25874): 117.88674885028797, (11, 25898): 110.92200999908347, (11, 25946): 119.03426156067539, (11, 26047): 86.43634025714023, (11, 26066): 47.50371796441707, (11, 26197): 67.64343482293552, (11, 26212): 178.41245516954646, (11, 26253): 184.73241278455376, (11, 26254): 182.2106437526006, (11, 26257): 180.35822628332753, (11, 26258): 183.56719714069263, (11, 26260): 181.88947459395652, (11, 26266): 183.53552055868673, (11, 26267): 181.66338183542572, (11, 26271): 181.6824135245697, (11, 26304): 159.53231992048816, (11, 26305): 159.62403602638312, (11, 26363): 124.3650376207047, (11, 26441): 329.3982051689881, (11, 26442): 329.0409525113577, (11, 26450): 325.7739721391055, (11, 26459): 324.26520180582565, (11, 26462): 324.1713998517918, (11, 26467): 333.56005634843433, (11, 26471): 331.5495698511698, (11, 26472): 331.45383612602905, (11, 26473): 331.5230399836666, (11, 26476): 331.8688094009743, (11, 26485): 326.4787852022983, (11, 26493): 327.2229064248574, (11, 26524): 325.02809837536216, (11, 26525): 324.99724860824443, (11, 26556): 330.22053860596003, (11, 26560): 328.88209709802067, (11, 26561): 326.6133828965605, (11, 26564): 329.6372561849215, (11, 26569): 326.4577600701024, (11, 26570): 326.04345695772054, (11, 26573): 327.11560250987645, (11, 26581): 327.5409783258432, (11, 26583): 326.5306369997691, (11, 26593): 328.1990637432926, (11, 26837): 334.69756647148165, (11, 26844): 336.6134142517439, (11, 26863): 333.66599344620954, (11, 26893): 339.66024417039665, (11, 26902): 342.30184207203285, (11, 26905): 338.5468537294378, (11, 26912): 340.9538919586558, (11, 26921): 336.4605402534598, (11, 26922): 332.96417325129124, (11, 27212): 327.0926195268088, (11, 27218): 323.72965327877813, (11, 27239): 331.34131616354483, (11, 27257): 329.5025421543971, (11, 27274): 332.3285408452369, (11, 27279): 332.18474172108347, (11, 27282): 329.76691401896625, (11, 27283): 330.1200976593521, (11, 27285): 333.6089247449292, (11, 27286): 331.93513436054894, (11, 27290): 327.75251146004183, (11, 27295): 325.79754489966507, (11, 27300): 332.6243896586531, (11, 27344): 327.56858288284946, (11, 27366): 330.6095173464238, (11, 27383): 334.4697691481895, (11, 27398): 336.66764998207134, (11, 27406): 334.03626037783647, (11, 27407): 334.50665221894997, (11, 27426): 329.2888267049621, (11, 27432): 319.4255911455893, (11, 27460): 325.32208448495186, (11, 27523): 336.557244922386, (11, 27545): 373.7746751727385, (11, 27602): 431.4325322426935, (11, 27606): 432.1191079906248, (11, 27646): 379.537009964411, (11, 27667): 390.8063963113581, (11, 27672): 391.1573810746392, (11, 27674): 389.3841537834775, (11, 27688): 390.0511910570364, (11, 27692): 393.38342252477173, (11, 27693): 391.7451776553387, (11, 27705): 391.9309219162962, (11, 27712): 392.96812500109655, (11, 27786): 425.68188005411315, (11, 27790): 416.57004488745537, (11, 27791): 415.6454229076413, (11, 27795): 422.7312873013348, (11, 27801): 416.17374930415184, (11, 27813): 427.74822356817634, (11, 27816): 425.1274700414799, (11, 27823): 415.901397417964, (11, 27830): 421.98670793013554, (11, 27884): 363.737197423586, (11, 27885): 375.24818907237466, (11, 27896): 368.1142537518532, (11, 27919): 367.35064726616, (11, 27922): 369.1952530709115, (11, 27930): 365.113031039346, (11, 27934): 365.80342721815464, (11, 27935): 366.4153118632148, (11, 27948): 437.4491659005427, (11, 27951): 436.5397418820824, (11, 28061): 419.98583732420184, (11, 28290): 525.5557201526052, (11, 28292): 528.8364836332821, (11, 28293): 526.2737893024905, (11, 28295): 525.9419512884921, (11, 28296): 525.7758551011882, (11, 28297): 523.8817518396025, (11, 28302): 523.638186173068, (11, 28310): 610.4954273931259, (11, 28313): 613.3813802369341, (11, 28372): 611.6269933478762, (11, 28398): 611.970533384338, (11, 28399): 611.3406631273483, (11, 28400): 612.6349875987397, (11, 28401): 608.9748303972509, (11, 28445): 612.8680545228414, (11, 28475): 604.8964525185949, (11, 28885): 113.39890563647236, (11, 28886): 111.85150017688822, (11, 28915): 108.86110298365428, (11, 28916): 109.43460282794696, (11, 28917): 108.30198308439331, (11, 28921): 115.41387998620398, (11, 28931): 114.28926358616494, (11, 28945): 98.96339888060169, (11, 28982): 103.75616323729521, (11, 29219): 89.16792801203421, (11, 29228): 86.69307124805081, (11, 29246): 98.55635361303233, (11, 29248): 95.66352949246898, (11, 29282): 91.62396862531767, (11, 29290): 103.51916942715044, (11, 29291): 101.86928364496424, (11, 29292): 103.03827485927413, (11, 29293): 101.35262250900718, (11, 29294): 101.58501156168346, (11, 29298): 100.77753144215555, (11, 29299): 99.92609752395875, (11, 29304): 99.95886714032615, (11, 29317): 97.18522640996638, (11, 29323): 97.07300692942226, (11, 29330): 98.2176430644157, (11, 29331): 99.44670913234467, (11, 29344): 82.79114137854212, (11, 29445): 50.389082632545744, (11, 29724): 806.4967405097586, (11, 29738): 807.4491237035357, (11, 29745): 804.760315988162, (11, 29748): 805.758086856512, (11, 29750): 807.5017384028579, (11, 29759): 804.3970262467142, (11, 29772): 807.9262336405479, (11, 29781): 807.1685240817039, (11, 29784): 806.3724003379388, (11, 29790): 808.0151477360055, (11, 29811): 806.2016174941864, (11, 29817): 813.839178073073, (11, 29818): 813.1070975044745, (11, 29929): 804.1421211566739, (11, 30039): 815.2143259401543, (11, 30066): 806.3850229991713, (11, 30116): 775.0812692344003, (11, 30238): 728.4340782884669, (11, 30248): 750.0170696508344, (11, 30260): 750.4101840082989, (11, 30545): 118.1746316485376, (11, 30733): 119.18624123413365, (11, 30756): 100.40064077104984, (11, 30921): 105.4730821012695, (11, 31079): 245.97283226726563, (11, 31149): 233.65172463055973, (11, 31154): 236.00137155929852, (11, 31160): 233.46611496777103, (11, 31163): 236.24064562229307, (11, 31189): 238.73169048474148, (11, 31215): 240.60014807741993, (11, 31259): 251.72240971410352, (11, 31262): 251.49656953801468, (11, 31430): 253.00794404639586, (11, 31568): 287.01262118787974, (11, 31751): 253.85308755958582, (13, 109): 202.30692340668955, (13, 872): 512.0928910453079, (13, 873): 514.4377041751221, (13, 877): 513.4128707352015, (13, 879): 513.7467830048757, (13, 884): 511.0669552696537, (13, 889): 512.6060935515025, (13, 891): 510.3290745229583, (13, 892): 515.5953981107656, (13, 894): 515.3582748207407, (13, 896): 513.340498898479, (13, 903): 513.3361791132439, (13, 909): 509.8219969916238, (13, 910): 510.8974583729671, (13, 912): 509.3155968395476, (13, 913): 507.5220353005419, (13, 916): 506.9653017751441, (13, 926): 511.84699859232643, (13, 927): 511.09141358492604, (13, 948): 509.50188363126927, (13, 961): 511.44167544442126, (13, 962): 511.8031659196131, (13, 963): 512.1788211298912, (13, 967): 514.3867901516296, (13, 974): 512.7929854000596, (13, 998): 515.197659521818, (13, 1014): 568.2769410342675, (13, 1086): 510.5355878784214, (13, 1087): 510.7841393128904, (13, 1089): 508.3451808131615, (13, 1090): 509.2847084561224, (13, 1092): 512.6495952703098, (13, 1097): 509.97607927307297, (13, 1107): 514.6668622698027, (13, 1387): 189.7547917167539, (13, 1554): 159.18118561249375, (13, 1827): 617.3369313319315, (13, 1828): 617.6444669072689, (13, 1829): 617.9733057804189, (13, 1830): 617.3416419643753, (13, 1831): 617.6006564430462, (13, 1832): 617.3683649750961, (13, 1833): 617.4406994396031, (13, 1836): 617.2148382206077, (13, 1841): 618.6791590322938, (13, 1843): 618.0387843291205, (13, 1844): 618.280808225944, (13, 1845): 617.4804745784412, (13, 1847): 615.1404930772972, (13, 1848): 615.9743555517346, (13, 1849): 619.8411820375304, (13, 1850): 620.2906672067501, (13, 1851): 616.4969734139407, (13, 1852): 616.4586687841182, (13, 1854): 616.937099553027, (13, 1856): 614.8887364982887, (13, 1857): 615.8624911530916, (13, 1858): 619.530060426047, (13, 1861): 617.833773976673, (13, 1866): 614.7488431634372, (13, 1867): 618.8079304661047, (13, 1868): 618.3762313739, (13, 1870): 618.0817858658439, (13, 1871): 618.7765043082169, (13, 1875): 616.9621105611751, (13, 1880): 615.5026816676797, (13, 1882): 615.6072082005379, (13, 1883): 620.4367674262489, (13, 1889): 616.1098643006386, (13, 1893): 618.1845523163448, (13, 1894): 617.6153868647058, (13, 1899): 615.6517668166124, (13, 1900): 616.127106090508, (13, 1902): 619.2223497896632, (13, 1905): 619.927877613126, (13, 1907): 616.6507451677192, (13, 1910): 617.0600645709175, (13, 1917): 621.8823535266268, (13, 1920): 616.7975602204093, (13, 1935): 620.227747349088, (13, 1937): 620.8519685296343, (13, 1946): 614.552705729569, (13, 1949): 615.3433937609179, (13, 1950): 612.4920598342097, (13, 1951): 613.8119597224002, (13, 1952): 614.4903042134899, (13, 1953): 615.1376963022689, (13, 1954): 614.3713645975039, (13, 1958): 615.0236908537612, (13, 1960): 616.2153576005089, (13, 1968): 616.6863811751897, (13, 1969): 620.5753847862288, (13, 1974): 619.5406452383372, (13, 1975): 619.4655078557728, (13, 1979): 617.7999971811707, (13, 1980): 617.4649313054722, (13, 1981): 618.1112432298632, (13, 1985): 618.5972427312677, (13, 1994): 611.0366593234862, (13, 2011): 615.5108673704877, (13, 2019): 621.5092623120785, (13, 2020): 620.7139839301828, (13, 2029): 617.5151378562547, (13, 2030): 620.1657696035769, (13, 2032): 616.8991892580354, (13, 2033): 618.6892541044523, (13, 2034): 618.5691903629353, (13, 2036): 615.0278213695723, (13, 2037): 615.9481427490289, (13, 2038): 616.6459950053592, (13, 2042): 626.105827026572, (13, 2050): 618.3962147228511, (13, 2051): 618.1611267485906, (13, 2053): 618.4554053265591, (13, 2054): 619.2888138678231, (13, 2066): 617.5755289045446, (13, 2067): 617.6315374248978, (13, 2071): 609.5087911658236, (13, 2072): 611.1553474500419, (13, 2073): 607.098549650481, (13, 2074): 606.821108541866, (13, 2080): 604.0024271912059, (13, 2082): 612.0209005615585, (13, 2083): 612.8783737449786, (13, 2089): 611.2176753865908, (13, 2090): 612.034534910488, (13, 2092): 611.051113462858, (13, 2098): 605.1486471631162, (13, 2099): 606.0084859014027, (13, 2101): 604.8958508568531, (13, 2102): 609.3161281597284, (13, 2103): 607.8910783710066, (13, 2104): 607.0709680886152, (13, 2106): 613.3919488585282, (13, 2112): 605.4030066916956, (13, 2113): 609.8921933796375, (13, 2114): 610.8090236093032, (13, 2117): 613.9796229954349, (13, 2123): 611.1461254115081, (13, 2124): 612.0570111020891, (13, 2134): 609.2126146273334, (13, 2138): 611.9921394729247, (13, 2141): 609.6046321226158, (13, 2148): 609.9903684232347, (13, 2150): 607.3416837275222, (13, 2151): 608.2298487031364, (13, 2152): 606.7726095463154, (13, 2153): 610.3868186951041, (13, 2154): 606.671219535139, (13, 2155): 606.0787059329685, (13, 2156): 605.4895168151377, (13, 2157): 605.8758241587923, (13, 2160): 612.806114805189, (13, 2161): 606.5203960198696, (13, 2162): 610.193705764188, (13, 2163): 608.9449911690384, (13, 2164): 608.8032550237147, (13, 2168): 607.2209397732493, (13, 2172): 607.6417971821755, (13, 2174): 607.9993177585922, (13, 2178): 608.264443032009, (13, 2179): 607.6402277282166, (13, 2183): 611.8188926064798, (13, 2185): 611.8171876821796, (13, 2186): 611.1214316316172, (13, 2190): 613.0881207708603, (13, 2192): 611.8145765643665, (13, 2193): 612.1073392197461, (13, 2194): 610.8065872163606, (13, 2195): 610.4915673468695, (13, 2197): 612.03206589419, (13, 2205): 610.034127544607, (13, 2207): 607.4739272041867, (13, 2208): 608.8809914928889, (13, 2212): 612.7666614886218, (13, 2214): 584.2455927605555, (13, 2225): 587.0532319151935, (13, 2231): 583.564031177458, (13, 2278): 599.3726333554987, (13, 2284): 601.8888365136743, (13, 2285): 601.4338508202597, (13, 2291): 595.5525284398238, (13, 2292): 596.7524823135337, (13, 2307): 600.1146034544178, (13, 2313): 594.7278841049784, (13, 2317): 595.0079321070997, (13, 2319): 597.6218731325544, (13, 2321): 598.7615396174685, (13, 2323): 598.7725534694682, (13, 2326): 603.8283825244555, (13, 2327): 602.658804734858, (13, 2329): 601.8422222276783, (13, 2330): 600.8701404578605, (13, 2332): 602.71417304145, (13, 2344): 599.9870906077066, (13, 2346): 599.8079656014403, (13, 2361): 600.4141927223712, (13, 2368): 613.4362097570129, (13, 2374): 614.6272291419216, (13, 2375): 615.1196227443282, (13, 2377): 610.7222719664794, (13, 2378): 615.8765755435095, (13, 2379): 615.8652979021902, (13, 2380): 616.3965842752939, (13, 2383): 611.9956773241977, (13, 2385): 612.732221347901, (13, 2395): 612.9216580588842, (13, 2397): 615.2758890465767, (13, 2398): 609.3078812252252, (13, 2399): 610.977731802932, (13, 2400): 610.6190423932236, (13, 2402): 612.8261421615016, (13, 2403): 613.8185593952946, (13, 2404): 614.1254022680555, (13, 2405): 611.6878024692352, (13, 2407): 613.7479466156393, (13, 2408): 614.8593847355917, (13, 2409): 612.446772583086, (13, 2411): 613.6041858200686, (13, 2412): 613.4211923354749, (13, 2413): 614.207290792291, (13, 2414): 612.8549046563012, (13, 2422): 613.2298124111342, (13, 2424): 613.746927831131, (13, 2426): 614.0042934503332, (13, 2433): 612.0707818315539, (13, 2436): 611.4419172143695, (13, 2437): 605.6763401322543, (13, 2440): 606.9840651164061, (13, 2445): 631.6172872870568, (13, 2447): 628.5599527544542, (13, 2454): 631.5464752275191, (13, 2455): 631.8076560754981, (13, 2460): 622.4082804731072, (13, 2461): 623.5472386929004, (13, 2471): 641.5517785155972, (13, 2492): 618.4129381784193, (13, 2511): 609.6039675949663, (13, 2523): 614.092596093588, (13, 2525): 612.5012751379147, (13, 2535): 616.7671099528427, (13, 2537): 614.6431513310248, (13, 2538): 616.2032999969367, (13, 2539): 615.1352240029645, (13, 2540): 617.7187965984208, (13, 2542): 619.0942336199838, (13, 2559): 649.5943374653366, (13, 2575): 646.3664510680526, (13, 2599): 603.0561288188653, (13, 2600): 612.7083504777623, (13, 2607): 607.5220427780256, (13, 2627): 613.875663283957, (13, 2647): 619.0968490594643, (13, 2674): 616.7120716655261, (13, 2681): 615.7332819314986, (13, 2683): 618.5115539045165, (13, 2686): 615.5370247157445, (13, 2689): 651.1407898918123, (13, 2690): 651.2659803275099, (13, 2713): 656.8440598882299, (13, 2714): 657.2790968378997, (13, 2715): 658.171407523129, (13, 2739): 657.4294135183492, (13, 2740): 652.2824586283386, (13, 2741): 652.7609907865893, (13, 2749): 656.0219601155727, (13, 2750): 656.3595458413178, (13, 2752): 657.0225040997786, (13, 2755): 657.6907347955969, (13, 2758): 657.4355812412966, (13, 2759): 657.464952475718, (13, 2769): 656.4958264243123, (13, 2771): 653.5947806495379, (13, 2779): 653.4338882212727, (13, 2784): 643.2150176965241, (13, 2800): 644.6044725850765, (13, 2802): 650.317574773341, (13, 2803): 650.0339368121201, (13, 2804): 649.4605710832104, (13, 2805): 650.9031478999106, (13, 2807): 650.9025046404855, (13, 2809): 650.4485449278221, (13, 2812): 644.8692752210242, (13, 2814): 649.7947414812949, (13, 2817): 649.5371319277798, (13, 2819): 651.1546292865193, (13, 2823): 644.9583430862267, (13, 2832): 651.9331736696859, (13, 2836): 647.9277889244971, (13, 2839): 650.9457491331292, (13, 2841): 649.962262146736, (13, 2843): 649.746086064759, (13, 2846): 648.5011646240433, (13, 2849): 652.4670477811329, (13, 2852): 651.591790510107, (13, 2853): 652.8666791942214, (13, 2876): 653.0255598127508, (13, 2877): 656.2044286657015, (13, 2885): 656.7000535669004, (13, 2918): 651.9707009013908, (13, 2921): 653.2838601329901, (13, 2925): 647.3145806009908, (13, 2926): 645.4382361008458, (13, 2930): 649.3900530943332, (13, 2931): 647.7494073064851, (13, 2938): 651.8894956826144, (13, 2940): 656.3704415373284, (13, 2947): 651.7853996621303, (13, 2949): 649.571741575726, (13, 2950): 650.095324338628, (13, 2952): 649.4110597031352, (13, 2958): 649.3180895272517, (13, 2959): 650.087682114373, (13, 2960): 651.5674911758913, (13, 2961): 650.7942879989859, (13, 2963): 648.6847875543237, (13, 2968): 649.0612649219837, (13, 2976): 648.5622362754697, (13, 2981): 634.9082423061877, (13, 2982): 634.42607318242, (13, 2984): 633.7254556816683, (13, 3003): 632.4205097045093, (13, 3046): 624.8592757627129, (13, 3050): 631.1787492322874, (13, 3051): 631.7561285472434, (13, 3053): 630.2176347703263, (13, 3069): 638.3695394509197, (13, 3071): 630.1178847778265, (13, 3080): 656.557816260074, (13, 3199): 629.6002650133356, (13, 3200): 627.9573785076377, (13, 3205): 637.7440181484184, (13, 3209): 628.771854107442, (13, 3215): 628.1066284458359, (13, 3217): 626.148324921233, (13, 3249): 628.3393733394086, (13, 3263): 643.1501797418645, (13, 3289): 633.1589725652859, (13, 3301): 633.4929267722289, (13, 3302): 632.8371281492574, (13, 3307): 631.9722532938359, (13, 3310): 634.335795214266, (13, 3391): 634.0328994232246, (13, 3509): 322.6663412181744, (13, 3510): 321.29019441728843, (13, 3511): 322.33512395825556, (13, 3512): 321.5977613596886, (13, 3514): 321.9905459911733, (13, 3519): 325.290865114677, (13, 3536): 325.32005013195925, (13, 3545): 327.61004692263344, (13, 3548): 325.6719540276379, (13, 3572): 325.9457785578758, (13, 3581): 323.85953567988287, (13, 3583): 323.4417983290833, (13, 3601): 327.69604207886977, (13, 3656): 325.0167258220387, (13, 3669): 321.4293519899615, (13, 3670): 322.6331418060879, (13, 3695): 315.9160808434146, (13, 3696): 316.9099143019535, (13, 3782): 328.6461646273529, (13, 3792): 326.7382975343426, (13, 3989): 267.5222884112359, (13, 4008): 274.6572857934574, (13, 4031): 273.4760050212993, (13, 4045): 271.62317748310886, (13, 4144): 272.73984126756426, (13, 4145): 266.50040791868196, (13, 4164): 270.19393898816696, (13, 4168): 268.3902425526942, (13, 4173): 268.1482743882937, (13, 4181): 263.8501483687177, (13, 4228): 258.83030773451, (13, 4248): 258.4014410878523, (13, 4254): 226.69934225375792, (13, 4260): 226.1331720263299, (13, 4262): 228.89042505248065, (13, 4273): 227.94730890062542, (13, 4319): 210.6979599717968, (13, 4326): 209.832007089863, (13, 4328): 209.8649099309267, (13, 4334): 211.79197314664384, (13, 4335): 211.4612685866093, (13, 4372): 308.5798763771557, (13, 4413): 333.5650659362559, (13, 4434): 306.69531826456904, (13, 4447): 306.54075300422124, (13, 4452): 307.4686392153014, (13, 4463): 286.0862336923281, (13, 4465): 286.09907034534604, (13, 4619): 345.2289430513711, (13, 4645): 347.63209242456145, (13, 4657): 348.17038795994296, (13, 4666): 347.71080482985747, (13, 4676): 350.35019547236595, (13, 4678): 350.40171015507286, (13, 4689): 349.9551644812903, (13, 4704): 363.42002550114205, (13, 4726): 419.3046321603262, (13, 4727): 418.3756941669311, (13, 4730): 416.5053251764989, (13, 4731): 417.49413215682915, (13, 4734): 415.93101776320464, (13, 4735): 415.43796641548755, (13, 4736): 416.21876544102673, (13, 4737): 415.1151101460971, (13, 4738): 415.5962374972371, (13, 4756): 416.7322544342352, (13, 4760): 410.1725843590306, (13, 4761): 409.93895752583416, (13, 4762): 409.3636525922274, (13, 4765): 410.8575613533716, (13, 4773): 420.75696298682277, (13, 4774): 420.5368038175563, (13, 4790): 420.0489903457093, (13, 4795): 419.08581983920936, (13, 4799): 421.2602932206107, (13, 4801): 424.0359088315676, (13, 4804): 418.64181860575155, (13, 4805): 417.8593556027096, (13, 4806): 421.0823528932002, (13, 4815): 420.7300367824667, (13, 4816): 422.775970858647, (13, 4817): 423.9368530593098, (13, 4826): 422.3378804517244, (13, 4830): 421.32058745843204, (13, 4839): 412.9131782062046, (13, 4840): 414.04306055459824, (13, 4841): 412.33206258697373, (13, 4846): 411.5696533242289, (13, 4848): 411.96707187686394, (13, 4850): 412.9140040006215, (13, 4871): 399.3575293483819, (13, 4883): 408.24238846075474, (13, 4900): 402.820107873615, (13, 4901): 402.14956331299067, (13, 4917): 357.5980681758229, (13, 4931): 351.7290132163815, (13, 4944): 357.78100697026275, (13, 4956): 353.2901226373897, (13, 4958): 354.08394970998006, (13, 4959): 353.63560985927427, (13, 4961): 354.08473914800214, (13, 4966): 352.41765211435927, (13, 5207): 346.0476261808612, (13, 5272): 200.17484270126633, (13, 5283): 202.68988982431392, (13, 5287): 209.39059115662187, (13, 5289): 210.58878977575145, (13, 5293): 197.9884116608516, (13, 5295): 204.67854979348047, (13, 5296): 206.25033555325865, (13, 5298): 207.07858670350137, (13, 5303): 210.43585987941344, (13, 5305): 202.04511467054402, (13, 5306): 202.6106976790671, (13, 5307): 200.96061567861884, (13, 5308): 203.6821687347219, (13, 5313): 201.46604368802906, (13, 5314): 202.3364571243391, (13, 5317): 204.79720234478307, (13, 5319): 208.54608775961626, (13, 5324): 205.95112996646853, (13, 5326): 204.18469101096602, (13, 5348): 203.53695361331646, (13, 5351): 207.6737241052016, (13, 5399): 214.3352485416802, (13, 5413): 214.4464828872507, (13, 5422): 213.96817126931722, (13, 5445): 209.34060830936832, (13, 5448): 207.13936307037844, (13, 5456): 208.40561416544662, (13, 5467): 210.91633020651878, (13, 5624): 180.9916633705106, (13, 5671): 233.76466339878004, (13, 5672): 230.40048419620337, (13, 5797): 272.63783555040817, (13, 5871): 260.4229730167282, (13, 5976): 235.89269397885397, (13, 6118): 485.7299544556108, (13, 6248): 515.5934246544551, (13, 6345): 24.0, (13, 6352): 24.0, (13, 6354): 24.0, (13, 6359): 24.0, (13, 6376): 24.0, (13, 6378): 24.0, (13, 6381): 24.0, (13, 6383): 24.0, (13, 6396): 24.0, (13, 6399): 24.0, (13, 6408): 24.0, (13, 6409): 24.0, (13, 6419): 24.0, (13, 6422): 24.0, (13, 6423): 24.0, (13, 6424): 24.0, (13, 6439): 24.0, (13, 6464): 24.0, (13, 6465): 24.0, (13, 6469): 24.0, (13, 6470): 24.0, (13, 6472): 24.0, (13, 6480): 24.0, (13, 6486): 24.0, (13, 6497): 24.0, (13, 6503): 24.0, (13, 6508): 24.0, (13, 6509): 24.0, (13, 6521): 24.0, (13, 6544): 24.0, (13, 6552): 24.0, (13, 6553): 24.0, (13, 6554): 24.0, (13, 6578): 24.0, (13, 6582): 24.0, (13, 6601): 24.0, (13, 6609): 24.0, (13, 6610): 24.0, (13, 6611): 24.0, (13, 6614): 24.0, (13, 6615): 24.0, (13, 6616): 24.0, (13, 6617): 24.0, (13, 6618): 24.0, (13, 6619): 24.0, (13, 6620): 24.0, (13, 6621): 24.0, (13, 6622): 24.0, (13, 6623): 24.0, (13, 6624): 24.0, (13, 6625): 24.0, (13, 6626): 24.0, (13, 6627): 24.0, (13, 6628): 24.0, (13, 6629): 24.0, (13, 6630): 24.0, (13, 6632): 24.0, (13, 6634): 24.0, (13, 6635): 24.0, (13, 6636): 24.0, (13, 6637): 24.0, (13, 6638): 24.0, (13, 6639): 24.0, (13, 6640): 24.0, (13, 6641): 24.0, (13, 6642): 24.0, (13, 6643): 24.0, (13, 6645): 24.0, (13, 6646): 24.0, (13, 6647): 24.0, (13, 6653): 24.0, (13, 6655): 24.0, (13, 6658): 24.0, (13, 6662): 24.0, (13, 6819): 53.27236922552736, (13, 6996): 48.74584727903285, (13, 7059): 41.87686739010169, (13, 7187): 89.11976739660278, (13, 7304): 84.17611279645148, (13, 7528): 64.11915684915682, (13, 7720): 54.056036532590994, (13, 7793): 59.38386623108267, (13, 7807): 57.897861170181265, (13, 7808): 60.67244441878741, (13, 7831): 24.0, (13, 7850): 24.0, (13, 7852): 24.0, (13, 8012): 43.55877796063166, (13, 8125): 93.62724050735657, (13, 8208): 71.14415128746332, (13, 8392): 36.003928404820584, (13, 8651): 108.13785852941622, (13, 9088): 57.88951487995629, (13, 9443): 153.4581175918046, (13, 9444): 152.56627173239, (13, 9828): 210.5641365332451, (13, 9868): 200.347597870331, (13, 10180): 97.31880269887027, (13, 10256): 118.44683421714839, (13, 10276): 103.01753809157749, (13, 10378): 89.87948387326264, (13, 10676): 120.929135922162, (13, 10714): 122.6114856924314, (13, 10730): 101.42548379283151, (13, 10862): 295.00247578769205, (13, 10881): 296.9320212815353, (13, 10883): 297.36220304421073, (13, 10885): 294.4307023255156, (13, 10891): 298.05409926627874, (13, 10909): 296.3431535815421, (13, 10911): 295.0324015353376, (13, 10913): 295.09550726765974, (13, 10915): 294.25849748491396, (13, 10919): 293.8430352781003, (13, 11037): 301.88870522771714, (13, 11039): 290.9283876265271, (13, 11516): 341.71408838224346, (13, 11856): 212.48818827746314, (13, 11857): 212.40956308736443, (13, 11861): 212.50344037198798, (13, 11881): 210.09785498555001, (13, 11902): 205.1704428900787, (13, 11911): 203.37718271562937, (13, 11914): 204.45177189895443, (13, 11922): 208.4284220080094, (13, 11924): 209.3622168111571, (13, 11926): 207.88766604778652, (13, 11950): 209.74638003444784, (13, 11963): 214.5438513241778, (13, 11983): 209.86228473593474, (13, 11985): 217.02841849256438, (13, 12009): 214.83213868273867, (13, 12010): 211.73565943493588, (13, 12018): 212.12627217935056, (13, 12020): 213.22970142869883, (13, 12021): 213.6546040987206, (13, 12024): 216.90140797579042, (13, 12025): 216.05922124622586, (13, 12027): 215.22720119081876, (13, 12031): 211.17508381303296, (13, 12032): 212.50424215464145, (13, 12035): 214.33260735446137, (13, 12041): 218.21219748252776, (13, 12045): 172.01470178409306, (13, 12145): 191.2595174481624, (13, 12275): 269.3202748504397, (13, 12294): 260.46876725258966, (13, 12358): 287.3644076232372, (13, 12463): 297.80722414001997, (13, 12465): 297.50027459800503, (13, 12482): 302.0430621053766, (13, 12503): 301.4079042075789, (13, 12506): 302.65176186829154, (13, 12549): 299.9766364563272, (13, 12559): 299.0155013119015, (13, 12569): 300.0276332218391, (13, 12572): 300.9644116698872, (13, 12574): 299.00831603589006, (13, 12576): 301.06916429681564, (13, 12591): 300.89963955349884, (13, 12608): 308.56758958207035, (13, 12696): 296.4370368404247, (13, 12710): 303.7459339877849, (13, 12728): 300.08155606109256, (13, 12766): 96.84059718849109, (13, 12771): 86.21940211756956, (13, 12790): 85.00863067577963, (13, 12795): 82.38358909702653, (13, 12797): 69.86924534229723, (13, 12798): 71.50010511665715, (13, 12811): 81.096382776134, (13, 12830): 77.98732694563436, (13, 12848): 79.49350138828152, (13, 12850): 80.29682706684396, (13, 12852): 77.45943306996963, (13, 12854): 75.98800319855091, (13, 12859): 80.9434881636702, (13, 12861): 73.10122850806482, (13, 12865): 83.00109785028368, (13, 12866): 82.17332096801545, (13, 12867): 85.18393315808358, (13, 12874): 83.73164013921682, (13, 12875): 84.81519250362787, (13, 12881): 80.33569137630705, (13, 12883): 82.14611393230088, (13, 12885): 85.79689583156421, (13, 12888): 81.25160918413113, (13, 12889): 80.79791627129222, (13, 12892): 84.07676495731353, (13, 12893): 81.3717711353283, (13, 12896): 82.19451886105394, (13, 12906): 84.1363805992227, (13, 13018): 76.58435763531469, (13, 13071): 78.73671346972047, (13, 13131): 60.77160022069812, (13, 13146): 69.4160466000067, (13, 13159): 66.00801455997566, (13, 13193): 58.58706113020538, (13, 13198): 40.28888974618463, (13, 13292): 59.45553837686442, (13, 13296): 65.02357146323898, (13, 13406): 35.04537661844497, (13, 13407): 35.193035616351445, (13, 13417): 39.85114349306257, (13, 13418): 42.13957147051906, (13, 13438): 43.65936091874263, (13, 13442): 43.46457990620195, (13, 13443): 42.39904450948201, (13, 13764): 123.63317546716179, (13, 13766): 122.14721439669378, (13, 13771): 125.78386481950959, (13, 13783): 121.34236040133311, (13, 13784): 119.58755545045362, (13, 13792): 131.93785373550816, (13, 13824): 122.80990872774024, (13, 14017): 101.9410633257168, (13, 14870): 261.8834802902557, (13, 14997): 96.01724592332522, (13, 15000): 97.29769750966851, (13, 15003): 98.1047388898797, (13, 15006): 90.66415451180929, (13, 15007): 90.21515262963585, (13, 15056): 94.52120831302993, (13, 15063): 95.85218017881489, (13, 15069): 97.65762953537923, (13, 15076): 91.11720222526309, (13, 15086): 91.24337687361992, (13, 15087): 93.81623721774264, (13, 15111): 94.44418818949912, (13, 15116): 94.19547124898007, (13, 15722): 114.07567994707266, (13, 15998): 157.37147451224152, (13, 16073): 380.2923930020604, (13, 16939): 537.7225071113253, (13, 16940): 535.9837906893199, (13, 16951): 537.6254172410108, (13, 16963): 537.8755668120799, (13, 16965): 540.141494611216, (13, 16969): 539.4166736736624, (13, 16970): 538.7613155332309, (13, 16971): 536.7319082777681, (13, 16973): 536.4751111189131, (13, 16974): 540.9365888556007, (13, 16976): 538.995592680007, (13, 16978): 537.5554606266576, (13, 16980): 539.8497437616347, (13, 16982): 540.7956250651902, (13, 17045): 594.9870040299587, (13, 17048): 597.5418047847461, (13, 17304): 249.5562830589178, (13, 17305): 247.71933111387625, (13, 17330): 249.08085500371595, (13, 17334): 247.25983940556125, (13, 17343): 250.77130844759412, (13, 17345): 246.5334106860634, (13, 17347): 248.51520816791316, (13, 17351): 243.9934609845647, (13, 17372): 246.74610294259443, (13, 17373): 250.72319476335332, (13, 17377): 250.9529994573534, (13, 17382): 248.2263454610684, (13, 17383): 248.94256276269385, (13, 17389): 247.28463683507948, (13, 17400): 250.15971821960028, (13, 17401): 250.2056753649391, (13, 17402): 250.2603276852978, (13, 17403): 250.48146813857966, (13, 17440): 246.0460126447444, (13, 17455): 249.89636124439676, (13, 17491): 249.72951716628003, (13, 17507): 247.2409771303839, (13, 17509): 248.95513597984683, (13, 17590): 242.24345468084843, (13, 17615): 238.60454612163693, (13, 17642): 239.68264192709987, (13, 17643): 239.2238415243155, (13, 17668): 238.75702910730837, (13, 17721): 237.24551819340675, (13, 17754): 251.9972655171765, (13, 17769): 248.6098487960578, (13, 17776): 241.14433836886326, (13, 17804): 251.23094476776868, (13, 17809): 252.76940931086244, (13, 17824): 252.26310340914384, (13, 17837): 245.56487127118294, (13, 17838): 245.33690637623587, (13, 17862): 243.99963343750997, (13, 17866): 247.479541377825, (13, 17872): 243.12619432322273, (13, 17873): 240.37898050722865, (13, 17881): 244.5355028020333, (13, 17947): 400.2590925309916, (13, 17951): 396.63573276383823, (13, 17953): 396.1042841478652, (13, 17954): 396.4636236510253, (13, 17959): 399.23952932197466, (13, 17963): 397.6884974798883, (13, 18000): 379.7258010350395, (13, 18001): 380.65818197047764, (13, 18111): 439.3619109283081, (13, 18148): 350.74850360431805, (13, 18166): 386.265241003954, (13, 18189): 416.84017376672494, (13, 18239): 251.74890486757263, (13, 18240): 251.65077960767567, (13, 18245): 251.85303803749048, (13, 18247): 251.42813708811371, (13, 18251): 251.75063652351466, (13, 18256): 252.00858717332903, (13, 18258): 251.57275133943676, (13, 18259): 251.60095772531704, (13, 18260): 251.69389987368805, (13, 18262): 251.92836538039393, (13, 18263): 252.0664107049961, (13, 18264): 252.1637434805611, (13, 18266): 251.97542803290378, (13, 18267): 252.08243707473756, (13, 18268): 252.1064780407944, (13, 18269): 252.3124811048737, (13, 18275): 252.21485134583511, (13, 18285): 252.16143471252886, (13, 18308): 250.058716901766, (13, 18313): 249.12420443257886, (13, 18314): 249.28898350495348, (13, 18315): 252.51381797077264, (13, 18316): 252.39116693672366, (13, 18317): 252.48092209384578, (13, 18320): 252.71412217496066, (13, 18321): 252.71700121132264, (13, 18322): 252.879484288419, (13, 18324): 253.15788469680285, (13, 18325): 253.80524106623, (13, 18326): 253.56873666464114, (13, 18327): 252.4782518604689, (13, 18329): 254.21048615394986, (13, 18330): 253.56990869725257, (13, 18331): 253.18583588351675, (13, 18332): 252.73823036123434, (13, 18333): 253.59227421268656, (13, 18336): 253.381621399638, (13, 18337): 253.66715380747624, (13, 18403): 252.77023623725378, (13, 18432): 241.1895852657297, (13, 18451): 248.98877171167675, (13, 18466): 257.00380990736943, (13, 18481): 252.95733714701947, (13, 18483): 252.8836113358318, (13, 18484): 252.5845998176048, (13, 18485): 251.76374719170948, (13, 18486): 252.98258306758197, (13, 18487): 252.25176727058508, (13, 18489): 252.628849575637, (13, 18490): 253.65495676983613, (13, 18491): 254.04317861084797, (13, 18492): 251.36002414657744, (13, 18493): 252.93528530044654, (13, 18494): 252.41065263868003, (13, 18495): 253.37701697951627, (13, 18496): 252.9085197395441, (13, 18497): 252.15472482917073, (13, 18498): 252.03371918104074, (13, 18499): 252.60981355461163, (13, 18501): 252.326327579983, (13, 18502): 251.9671322291718, (13, 18503): 251.59894618694162, (13, 18504): 252.97687289135612, (13, 18506): 252.600515899864, (13, 18507): 252.30264906703587, (13, 18508): 252.6024560315309, (13, 18509): 252.6813982012891, (13, 18510): 251.71479655685192, (13, 18511): 253.20182877988938, (13, 18512): 252.6220020251601, (13, 18515): 253.11804195397704, (13, 18516): 253.39517887801077, (13, 18517): 253.0514934209805, (13, 18518): 253.63327554778928, (13, 18519): 253.01400445828804, (13, 18520): 252.40354373859014, (13, 18522): 254.45208850255713, (13, 18523): 254.61347410615778, (13, 18532): 255.2504986945618, (13, 18535): 254.0083453612612, (13, 18537): 253.31678866929664, (13, 18539): 253.50270278394825, (13, 18540): 253.62699219688875, (13, 18541): 254.0037190346552, (13, 18542): 254.23537478694124, (13, 18543): 253.1172088030586, (13, 18546): 253.78380312510154, (13, 18555): 254.87560401066992, (13, 18556): 255.12892676338447, (13, 18565): 255.27654255844666, (13, 18567): 255.75176900668697, (13, 18568): 255.08947834965258, (13, 18577): 259.3254788974763, (13, 18583): 258.39713384266787, (13, 18605): 259.03033692579055, (13, 18608): 256.4392426620582, (13, 18616): 262.9993057640893, (13, 18618): 266.51325803521127, (13, 18625): 264.7994100304685, (13, 18645): 261.5967682578434, (13, 18646): 262.552117873629, (13, 18653): 260.26703470836725, (13, 18654): 263.00538597095886, (13, 18655): 261.32198914400044, (13, 18666): 271.3540667012259, (13, 18837): 253.969368230808, (13, 18974): 247.44512876730744, (13, 18999): 249.57391239492463, (13, 19000): 250.57302340499518, (13, 19174): 201.1583904218499, (13, 19342): 221.24981993396523, (13, 19455): 209.6782693628509, (13, 19555): 160.16776026234822, (13, 19564): 163.66109970239796, (13, 19573): 161.38101102264193, (13, 19586): 160.32674914362457, (13, 19605): 161.02492549335446, (13, 19611): 162.5187633621184, (13, 19614): 161.7011243801701, (13, 19641): 185.94166429953734, (13, 19702): 185.72363196327265, (13, 19713): 183.89973006453687, (13, 19731): 152.15153199139763, (13, 19819): 201.93279171720178, (13, 19893): 198.16705868427724, (13, 19899): 212.56504196361053, (13, 19929): 200.6947197998503, (13, 19951): 224.9339458557722, (13, 19962): 205.0554506015652, (13, 19970): 205.5910359632583, (13, 19971): 206.78379139124084, (13, 19972): 205.54743410028155, (13, 19975): 203.8236248475031, (13, 19978): 225.3587941989439, (13, 19987): 225.1004000462281, (13, 19989): 218.4545305265504, (13, 20039): 225.99787957721767, (13, 20043): 227.86091664473656, (13, 20047): 224.93436465883698, (13, 20052): 218.31519626199182, (13, 20054): 219.32845680684534, (13, 20085): 246.85044276018397, (13, 20104): 248.75018170374207, (13, 20132): 237.98630336462975, (13, 20203): 207.6205755625583, (13, 20280): 208.63278970947397, (13, 20285): 209.5226927423571, (13, 20290): 209.0236168164778, (13, 20297): 206.60801362137798, (13, 20309): 234.3873774275506, (13, 20453): 261.30790725580323, (13, 20485): 191.81746862412885, (13, 20520): 185.561526636065, (13, 20526): 187.48899766309944, (13, 20698): 201.10705449306388, (13, 20868): 259.2038203658075, (13, 21042): 94.38464674471804, (13, 21057): 105.02426983984638, (13, 21066): 100.95647366538506, (13, 21075): 97.1982685668271, (13, 21093): 96.99669698165795, (13, 21098): 106.96072417666355, (13, 21127): 96.19876438059785, (13, 21130): 99.03680480128945, (13, 21144): 97.05303138034891, (13, 21146): 95.51898009346836, (13, 21147): 96.3872609690573, (13, 21148): 98.79682968068448, (13, 21153): 88.52847381117583, (13, 21293): 114.30608635541392, (13, 21426): 101.43724523103616, (13, 21442): 114.24911369128277, (13, 21451): 115.535456443941, (13, 21466): 107.92457221712583, (13, 21469): 110.01687830069048, (13, 21471): 106.85412300992198, (13, 21473): 108.63741213239729, (13, 21475): 107.10149660174281, (13, 21482): 111.16550712670352, (13, 21484): 110.81941462761915, (13, 21488): 109.54676923815133, (13, 21494): 107.35620322168911, (13, 21498): 108.84591658239553, (13, 21500): 106.72412307505341, (13, 21514): 112.11228927442109, (13, 21537): 107.05785792563634, (13, 21662): 115.05108610698194, (13, 21691): 107.25692086455467, (13, 21757): 90.12553747504408, (13, 21777): 83.65628587473587, (13, 21778): 82.26804630009657, (13, 21779): 84.31114150459356, (13, 21790): 83.92867668295213, (13, 21802): 86.25883938077344, (13, 21824): 88.96324070351818, (13, 21874): 86.24321699531339, (13, 21879): 87.87053735661804, (13, 21983): 81.82406211704263, (13, 22002): 106.37331766463686, (13, 22132): 75.75846215140052, (13, 22261): 247.80174170420048, (13, 22298): 245.94922134004415, (13, 22339): 273.0616372303134, (13, 22508): 210.88567264737017, (13, 22841): 623.8108782669135, (13, 22842): 623.8639352231297, (13, 22874): 619.0634784079425, (13, 22941): 619.4218025658635, (13, 22956): 622.4828194803988, (13, 22960): 623.2711594352911, (13, 22968): 626.8492100857569, (13, 22970): 627.5918025475731, (13, 22974): 629.465369437018, (13, 22980): 633.1017411067446, (13, 23025): 633.2979722636456, (13, 23028): 632.6045300326692, (13, 23081): 639.4568773125033, (13, 23104): 633.982998543647, (13, 23147): 600.0799120920107, (13, 23298): 148.64449807019577, (13, 23376): 143.15799434810862, (13, 23381): 142.16138050173745, (13, 23529): 153.7868862691681, (13, 23556): 150.36927328368688, (13, 23718): 143.78903907193788, (13, 24001): 181.32500300891863, (13, 24094): 194.3362705490088, (13, 24129): 199.85695172884087, (13, 24174): 189.75565404333602, (13, 24235): 202.80127402076917, (13, 24259): 207.15558276026218, (13, 24260): 206.8902748112434, (13, 24261): 205.5879515935778, (13, 24305): 213.11355762100624, (13, 24306): 214.34313753173544, (13, 24307): 212.63822584506485, (13, 24308): 194.08790210439324, (13, 24498): 225.16109806987527, (13, 24499): 225.32585576212887, (13, 24500): 224.24002295254834, (13, 24668): 215.26589420807557, (13, 24711): 233.2317740367167, (13, 24756): 237.98672118919922, (13, 24788): 239.163406474575, (13, 24809): 234.01582193803773, (13, 24813): 235.50793379609416, (13, 24821): 234.9700105774454, (13, 24825): 235.56301726727128, (13, 24832): 233.51254474898613, (13, 24833): 234.401458915096, (13, 24835): 235.34794650786884, (13, 24837): 236.62709036739048, (13, 24840): 233.44894261960997, (13, 24841): 234.67095325308964, (13, 24844): 233.59012172930386, (13, 24845): 234.01145917822885, (13, 24846): 234.4821995506937, (13, 24849): 235.01398087536614, (13, 24850): 235.89834597893548, (13, 24863): 222.83001015557386, (13, 24866): 224.3708671511448, (13, 24885): 226.58707522544438, (13, 24886): 226.94860419936666, (13, 24889): 229.6426945641712, (13, 24903): 230.67503830046618, (13, 24909): 224.34342692840931, (13, 24999): 294.9588725652304, (13, 25019): 292.68208517881476, (13, 25028): 294.01348735316924, (13, 25137): 228.55750092842564, (13, 25145): 229.97156412095043, (13, 25208): 261.4016130348741, (13, 25233): 259.85061179675574, (13, 25371): 218.9451748272157, (13, 25377): 211.69890661034154, (13, 25828): 144.10434058952077, (13, 25851): 130.1260324554181, (13, 25874): 137.42762155036598, (13, 25898): 148.97334584423, (13, 25946): 142.99346816059958, (13, 26047): 174.19259985992227, (13, 26066): 161.94182336409068, (13, 26197): 161.59960414021825, (13, 26212): 169.81942337904974, (13, 26253): 173.49458864091653, (13, 26254): 171.3272706269935, (13, 26257): 172.4470388556708, (13, 26258): 173.43759202572204, (13, 26260): 172.74251651790976, (13, 26266): 168.68585042880594, (13, 26267): 168.69616889447192, (13, 26271): 169.34463265377403, (13, 26304): 155.00154493214617, (13, 26305): 153.29327412668204, (13, 26363): 153.72517192041025, (13, 26441): 282.3186433331083, (13, 26442): 281.38245002349646, (13, 26450): 278.5466652825818, (13, 26459): 279.76209330682747, (13, 26462): 280.79835700258735, (13, 26467): 289.3485818380766, (13, 26471): 286.2257885492665, (13, 26472): 285.7611026282468, (13, 26473): 285.45963103047967, (13, 26476): 282.01107101686, (13, 26485): 280.4945326527623, (13, 26493): 279.84810280964825, (13, 26524): 282.7242399215971, (13, 26525): 281.9928452522117, (13, 26556): 285.1354018911954, (13, 26560): 286.04795308853596, (13, 26561): 284.4838684298194, (13, 26564): 284.0203666022159, (13, 26569): 283.63690219701937, (13, 26570): 282.4436933356994, (13, 26573): 282.2751282572686, (13, 26581): 281.6466715732271, (13, 26583): 281.35618769458125, (13, 26593): 280.96097068492935, (13, 26837): 289.36697057307094, (13, 26844): 291.58890464274515, (13, 26863): 285.40640451354955, (13, 26893): 291.26641214762213, (13, 26902): 294.2441371018256, (13, 26905): 292.4157938257499, (13, 26912): 294.35980764638043, (13, 26921): 288.29343112532916, (13, 26922): 280.44151200103965, (13, 27212): 332.5297181354407, (13, 27218): 331.3756796344108, (13, 27239): 336.1776313514671, (13, 27257): 333.6800649692082, (13, 27274): 336.7182294392459, (13, 27279): 335.77848880968077, (13, 27282): 333.4946953885027, (13, 27283): 335.3706196614951, (13, 27285): 337.4538630619365, (13, 27286): 334.487415562269, (13, 27290): 331.4617393309125, (13, 27295): 330.8108479723441, (13, 27300): 337.3095363271234, (13, 27344): 328.93194123856426, (13, 27366): 331.0322777332659, (13, 27383): 336.6098097090788, (13, 27398): 340.6143980075177, (13, 27406): 338.70273692098675, (13, 27407): 339.7771351020577, (13, 27426): 340.19455811056, (13, 27432): 329.3250743636491, (13, 27460): 336.60022190236293, (13, 27523): 324.1342053284189, (13, 27545): 373.68487956149744, (13, 27602): 423.57271367941394, (13, 27606): 425.04243114099336, (13, 27646): 361.7998882303251, (13, 27667): 372.10643540324617, (13, 27672): 372.97051422363234, (13, 27674): 371.0106893884758, (13, 27688): 373.7606969822959, (13, 27692): 374.3880365152511, (13, 27693): 372.7744603184148, (13, 27705): 372.32737623209283, (13, 27712): 372.81306201711476, (13, 27786): 438.3364947073099, (13, 27790): 436.8175585772988, (13, 27791): 436.9594417326842, (13, 27795): 435.0448297917301, (13, 27801): 433.51417378896883, (13, 27813): 439.4512421870193, (13, 27816): 438.4064451485793, (13, 27823): 433.49660714143073, (13, 27830): 437.1002569727225, (13, 27884): 340.7825916739654, (13, 27885): 356.89575580770526, (13, 27896): 347.3623904509515, (13, 27919): 347.0682254264285, (13, 27922): 348.5316234633946, (13, 27930): 343.70638724612263, (13, 27934): 343.99643091573114, (13, 27935): 344.0786348047792, (13, 27948): 402.7930467661847, (13, 27951): 410.67374196594136, (13, 28061): 317.7591522509461, (13, 28290): 441.0125417410533, (13, 28292): 442.33770312316904, (13, 28293): 441.17920235334867, (13, 28295): 439.43344151310095, (13, 28296): 440.50414892056995, (13, 28297): 440.2351875581263, (13, 28302): 438.71632620853717, (13, 28310): 444.25087034024443, (13, 28313): 445.61303911474687, (13, 28372): 446.8929572321045, (13, 28398): 447.0101414191059, (13, 28399): 446.1655661823598, (13, 28400): 447.4068203445384, (13, 28401): 444.27432050838627, (13, 28445): 444.182608101781, (13, 28475): 442.50975541500645, (13, 28885): 207.64436826975964, (13, 28886): 206.8483021987665, (13, 28915): 208.6637235763725, (13, 28916): 207.49895961203788, (13, 28917): 207.15582979667215, (13, 28921): 209.35631774227502, (13, 28931): 209.31266026444905, (13, 28945): 207.6503713436495, (13, 28982): 207.67557440219676, (13, 29219): 219.58551862804103, (13, 29228): 214.8188608668142, (13, 29246): 249.18670988510087, (13, 29248): 250.11053682724656, (13, 29282): 243.24704485084382, (13, 29290): 251.0625879135093, (13, 29291): 250.10017960150847, (13, 29292): 251.184975914174, (13, 29293): 248.56450872150256, (13, 29294): 251.19768711231663, (13, 29298): 249.10413320039632, (13, 29299): 249.22997769294705, (13, 29304): 246.01417019635576, (13, 29317): 239.27949319554116, (13, 29323): 238.71804246368, (13, 29330): 242.02144724998337, (13, 29331): 243.3756016427429, (13, 29344): 222.83656901986635, (13, 29445): 177.0890659950438, (13, 29724): 612.7610532395439, (13, 29738): 613.7344664453814, (13, 29745): 610.7984084661869, (13, 29748): 610.8832240663831, (13, 29750): 612.2791256230864, (13, 29759): 609.6062815653067, (13, 29772): 613.1955219891767, (13, 29781): 612.3984656692664, (13, 29784): 611.9863520664077, (13, 29790): 613.0978651245421, (13, 29811): 610.8510999841177, (13, 29817): 616.3660522965837, (13, 29818): 615.5856169149957, (13, 29929): 610.7647895940388, (13, 30039): 624.9054171093566, (13, 30066): 617.6005417130907, (13, 30116): 583.2720591993977, (13, 30238): 532.7099857981195, (13, 30248): 559.0115876526348, (13, 30260): 559.7142020116178, (13, 30545): 188.47565899449103, (13, 30733): 135.42052907893898, (13, 30756): 129.8732711659961, (13, 30921): 150.42159177230351, (13, 31079): 45.46375155661722, (13, 31149): 28.240610716495706, (13, 31154): 30.92123504117032, (13, 31160): 27.83477763347279, (13, 31163): 30.787706239555906, (13, 31189): 31.20143852471655, (13, 31215): 32.45514635215098, (13, 31259): 43.12061695692921, (13, 31262): 43.15724727396482, (13, 31430): 54.097597661814, (13, 31568): 79.60961865687061, (13, 31751): 48.45089808447259, (15, 109): 173.44239952693607, (15, 872): 587.0814572580928, (15, 873): 589.5248901755738, (15, 877): 588.5998433070542, (15, 879): 588.9615635968405, (15, 884): 586.4884160440172, (15, 889): 588.0239051464745, (15, 891): 585.6817458845612, (15, 892): 590.8576614189669, (15, 894): 590.5524610438102, (15, 896): 588.2124733653487, (15, 903): 588.6824381946594, (15, 909): 584.5502239805975, (15, 910): 585.5373976813279, (15, 912): 583.9194695144262, (15, 913): 582.1333983154444, (15, 916): 581.3910447648298, (15, 926): 586.3507874158855, (15, 927): 585.5326611424066, (15, 948): 584.7971086845695, (15, 961): 586.2421532029599, (15, 962): 586.525592980587, (15, 963): 586.8422691239389, (15, 967): 589.7189528682869, (15, 974): 588.3898179439466, (15, 998): 590.6797636360056, (15, 1014): 644.1823414114916, (15, 1086): 581.3957114690771, (15, 1087): 581.1324346418197, (15, 1089): 578.8558985963509, (15, 1090): 579.8816568541738, (15, 1092): 583.4016108440757, (15, 1097): 580.7081477252777, (15, 1107): 585.1814763093207, (15, 1387): 218.9489768006022, (15, 1554): 181.05275620735011, (15, 1827): 698.6297276166335, (15, 1828): 698.8946609313168, (15, 1829): 699.2676287916978, (15, 1830): 698.8579395850898, (15, 1831): 699.0816166066613, (15, 1832): 698.819725141458, (15, 1833): 698.8529902155452, (15, 1836): 698.5744587943394, (15, 1841): 700.1402535638557, (15, 1843): 699.4819661005407, (15, 1844): 699.7714451940194, (15, 1845): 698.984500100792, (15, 1847): 696.4581297573587, (15, 1848): 697.3304084391617, (15, 1849): 701.415220460585, (15, 1850): 701.8467173466763, (15, 1851): 697.9883449317895, (15, 1852): 698.0441024898324, (15, 1854): 698.4683458456194, (15, 1856): 696.3230140527786, (15, 1857): 697.266263627462, (15, 1858): 701.0234327831505, (15, 1861): 699.2052536324195, (15, 1866): 696.2602194231296, (15, 1867): 700.1926932963449, (15, 1868): 699.6711221513144, (15, 1870): 699.6883889520202, (15, 1871): 700.0803876890515, (15, 1875): 698.4296007580795, (15, 1880): 696.8769932343068, (15, 1882): 697.1231930625288, (15, 1883): 701.8899222539004, (15, 1889): 697.3472226726667, (15, 1893): 699.3291031352045, (15, 1894): 698.7137605128505, (15, 1899): 696.8082275247135, (15, 1900): 697.2663454713417, (15, 1902): 700.4009315241003, (15, 1905): 701.1922348042846, (15, 1907): 697.9329087592877, (15, 1910): 698.2370789760752, (15, 1917): 702.896829264794, (15, 1920): 697.9999993674414, (15, 1935): 701.3172756961934, (15, 1937): 701.9934606058088, (15, 1946): 695.4543807924587, (15, 1949): 696.218441180237, (15, 1950): 693.5294471241128, (15, 1951): 694.8226492996507, (15, 1952): 695.7674308810159, (15, 1953): 696.2040829202324, (15, 1954): 695.584189809215, (15, 1958): 695.9939990180421, (15, 1960): 697.2803634455931, (15, 1968): 697.7880760957191, (15, 1969): 701.4885867573537, (15, 1974): 700.5195477533053, (15, 1975): 700.5048760550952, (15, 1979): 698.6788711020815, (15, 1980): 698.5224293677028, (15, 1981): 699.0662902637736, (15, 1985): 699.5113847135144, (15, 1994): 692.464450922144, (15, 2011): 697.0869144396829, (15, 2019): 703.4801421667294, (15, 2020): 702.6344941494125, (15, 2029): 699.4148013012367, (15, 2030): 702.0485239596032, (15, 2032): 698.8838296342885, (15, 2033): 700.5985833188756, (15, 2034): 700.5644722830303, (15, 2036): 697.3291750260959, (15, 2037): 698.1577324631531, (15, 2038): 698.4555094516121, (15, 2042): 708.2195384774086, (15, 2050): 700.165585070028, (15, 2051): 700.0197057758012, (15, 2053): 700.2810439824442, (15, 2054): 701.1447532840617, (15, 2066): 699.3862282489918, (15, 2067): 699.3944111952903, (15, 2071): 690.8378666454992, (15, 2072): 692.460293155944, (15, 2073): 688.0289313019167, (15, 2074): 687.8066246253298, (15, 2080): 685.0646842387155, (15, 2082): 693.3342097794807, (15, 2083): 694.1734223028585, (15, 2089): 692.398867147675, (15, 2090): 693.1823902430746, (15, 2092): 692.1184224370786, (15, 2098): 686.1159183695215, (15, 2099): 687.057271626378, (15, 2101): 685.9430757267276, (15, 2102): 690.3652186897308, (15, 2103): 688.9739083812226, (15, 2104): 688.2120405758395, (15, 2106): 694.7379723584793, (15, 2112): 686.5291423463068, (15, 2113): 690.993442004034, (15, 2114): 692.0561598086161, (15, 2117): 695.4000646507874, (15, 2123): 689.0294198333042, (15, 2124): 689.941170771294, (15, 2134): 687.3398707472807, (15, 2138): 690.023853880956, (15, 2141): 687.6567963446372, (15, 2148): 688.9820833557809, (15, 2150): 685.4371419281979, (15, 2151): 686.3959404017106, (15, 2152): 684.9322539872791, (15, 2153): 689.2904056766342, (15, 2154): 685.5131211992265, (15, 2155): 685.0772691288843, (15, 2156): 684.3750391180596, (15, 2157): 685.3312813467363, (15, 2160): 691.2939374920429, (15, 2161): 684.7739557893066, (15, 2162): 689.4476570982068, (15, 2163): 688.1669266869834, (15, 2164): 688.0810007268472, (15, 2168): 685.8012035039809, (15, 2172): 686.6503648016575, (15, 2174): 686.2844477454805, (15, 2178): 687.3981248370254, (15, 2179): 686.8082987305008, (15, 2183): 689.960376574552, (15, 2185): 690.0172673642838, (15, 2186): 689.2897629248594, (15, 2190): 691.4733878843406, (15, 2192): 690.1631838741835, (15, 2193): 690.2162988700057, (15, 2194): 688.8780840834437, (15, 2195): 688.6833937561786, (15, 2197): 690.4497166171769, (15, 2205): 688.5760197247012, (15, 2207): 686.1380411303829, (15, 2208): 687.5015200763588, (15, 2212): 690.6099696554176, (15, 2214): 663.5801934873518, (15, 2225): 666.7875504338609, (15, 2231): 660.5037035475618, (15, 2278): 680.103743562749, (15, 2284): 682.8570767076878, (15, 2285): 682.4717499031426, (15, 2291): 677.000961811662, (15, 2292): 677.600459351929, (15, 2307): 681.0666220757436, (15, 2313): 676.353506459529, (15, 2317): 675.568493602562, (15, 2319): 678.5475736052242, (15, 2321): 679.8113763476995, (15, 2323): 679.6465080060788, (15, 2326): 684.4674770632763, (15, 2327): 683.2750570105925, (15, 2329): 682.4608735450369, (15, 2330): 681.5326885575662, (15, 2332): 683.4958887590932, (15, 2344): 680.4592785010635, (15, 2346): 680.4014366831066, (15, 2361): 679.9615371551876, (15, 2368): 693.8549540135889, (15, 2374): 695.1655671046484, (15, 2375): 695.6057929409178, (15, 2377): 691.0256747503694, (15, 2378): 696.4314716402577, (15, 2379): 696.5445042739003, (15, 2380): 696.9987668683831, (15, 2383): 692.2497081814307, (15, 2385): 692.9581523277925, (15, 2395): 693.0394903209951, (15, 2397): 695.998584960896, (15, 2398): 689.5662883322578, (15, 2399): 691.2161220727407, (15, 2400): 690.8465216117797, (15, 2402): 693.4554607490005, (15, 2403): 694.4794185705867, (15, 2404): 694.7444764401981, (15, 2405): 692.2756607340199, (15, 2407): 694.2887519751495, (15, 2408): 695.4890324565233, (15, 2409): 693.0250387289932, (15, 2411): 694.4665892501155, (15, 2412): 694.1998779667296, (15, 2413): 695.0392571158083, (15, 2414): 693.6726511640314, (15, 2422): 694.1528704512996, (15, 2424): 694.4901614911926, (15, 2426): 694.7131800456265, (15, 2433): 692.8020851678123, (15, 2436): 692.2904560788617, (15, 2437): 686.3120210548097, (15, 2440): 687.6306686407598, (15, 2445): 714.0512992782789, (15, 2447): 710.8017770930859, (15, 2454): 713.8644883796275, (15, 2455): 714.038792480648, (15, 2460): 704.5230270350951, (15, 2461): 705.6965902206782, (15, 2471): 724.6513906180495, (15, 2492): 704.3391547527655, (15, 2511): 694.8399769997978, (15, 2523): 699.6966514060178, (15, 2525): 698.2483201366892, (15, 2535): 700.85905148724, (15, 2537): 698.7497524975882, (15, 2538): 700.2143897904817, (15, 2539): 699.554185083872, (15, 2540): 701.8147992507805, (15, 2542): 703.3261367220244, (15, 2559): 733.3588926550475, (15, 2575): 730.5942881366884, (15, 2599): 685.42470241745, (15, 2600): 695.5313189366708, (15, 2607): 689.7356917208144, (15, 2627): 700.5715192777446, (15, 2647): 706.1220545655219, (15, 2674): 703.2981016724023, (15, 2681): 702.5026126936693, (15, 2683): 705.2328673846513, (15, 2686): 702.11835251075, (15, 2689): 738.404501515964, (15, 2690): 738.5768117097579, (15, 2713): 745.5167326210776, (15, 2714): 746.1227078722047, (15, 2715): 747.0169882329111, (15, 2739): 746.2251651194199, (15, 2740): 740.6002755781584, (15, 2741): 741.0465392318431, (15, 2749): 744.9857027015497, (15, 2750): 745.2666677020496, (15, 2752): 745.905071194915, (15, 2755): 746.6114748066715, (15, 2758): 746.403967573262, (15, 2759): 746.4076088260554, (15, 2769): 745.3701058888932, (15, 2771): 742.0394365831029, (15, 2779): 742.3065759118368, (15, 2784): 732.230217029925, (15, 2800): 734.0304593148309, (15, 2802): 738.8607216779802, (15, 2803): 738.5216120134755, (15, 2804): 737.9241913761566, (15, 2805): 739.6113048604097, (15, 2807): 739.5563812026369, (15, 2809): 739.2213127450709, (15, 2812): 733.4797902502515, (15, 2814): 738.9163690893655, (15, 2817): 739.1170875090608, (15, 2819): 739.6758235393504, (15, 2823): 734.032926664224, (15, 2832): 740.7222696112188, (15, 2836): 736.6912212394082, (15, 2839): 739.5445332998713, (15, 2841): 739.3134807243971, (15, 2843): 739.0135362841478, (15, 2846): 737.4843790225783, (15, 2849): 741.3500464887197, (15, 2852): 740.4350251203742, (15, 2853): 741.7711959994116, (15, 2876): 742.1770737585645, (15, 2877): 745.4108428378937, (15, 2885): 746.3920314314229, (15, 2918): 740.14087621091, (15, 2921): 741.5307448674455, (15, 2925): 735.0114634384714, (15, 2926): 732.8375186575341, (15, 2930): 737.7400073150459, (15, 2931): 735.6096440100932, (15, 2938): 740.1568508860393, (15, 2940): 744.2069404898143, (15, 2947): 739.457585714288, (15, 2949): 737.7019830573901, (15, 2950): 738.3262032451647, (15, 2952): 737.6392702055113, (15, 2958): 737.5058646378318, (15, 2959): 738.16957120548, (15, 2960): 739.699052001544, (15, 2961): 738.963860423541, (15, 2963): 736.9232808011018, (15, 2968): 737.3598362991836, (15, 2976): 736.7412181024998, (15, 2981): 723.6738123336111, (15, 2982): 723.2990517218448, (15, 2984): 722.6199498847019, (15, 3003): 721.4288276762983, (15, 3046): 712.5210832632256, (15, 3050): 719.5120450525076, (15, 3051): 720.0491893738251, (15, 3053): 718.5499902867513, (15, 3069): 726.934050329049, (15, 3071): 718.1862987115703, (15, 3080): 746.4176812572233, (15, 3199): 719.2405346940683, (15, 3200): 717.6623923431615, (15, 3205): 727.4157927583575, (15, 3209): 718.4904812500782, (15, 3215): 717.7555644122755, (15, 3217): 715.8078363982091, (15, 3249): 717.92781610387, (15, 3263): 732.6328564452821, (15, 3289): 722.5604428916, (15, 3301): 723.0405166548138, (15, 3302): 722.3340126376871, (15, 3307): 721.4581582289544, (15, 3310): 723.8789707248832, (15, 3391): 726.056714113989, (15, 3509): 408.6392363186194, (15, 3510): 407.24683606802034, (15, 3511): 408.1783280261622, (15, 3512): 407.32107582563145, (15, 3514): 407.6177184824812, (15, 3519): 411.893448901747, (15, 3536): 411.10313655531945, (15, 3545): 413.2929178468957, (15, 3548): 411.1650303219877, (15, 3572): 411.8885738377723, (15, 3581): 410.1912319200948, (15, 3583): 409.2570310341452, (15, 3601): 414.5081432073878, (15, 3656): 412.2517644800709, (15, 3669): 409.56641936909654, (15, 3670): 410.8182138454361, (15, 3695): 403.6592013166532, (15, 3696): 404.64546455808244, (15, 3782): 411.8451185602711, (15, 3792): 410.2790453679283, (15, 3989): 190.19464332547443, (15, 4008): 197.87776733953555, (15, 4031): 197.97610798485965, (15, 4045): 194.6778495164696, (15, 4144): 194.61609695096845, (15, 4145): 186.5209785045611, (15, 4164): 191.54860788475975, (15, 4168): 188.9662519969289, (15, 4173): 188.3907081252569, (15, 4181): 183.74019142936007, (15, 4228): 179.75431450509714, (15, 4248): 177.32565997134196, (15, 4254): 136.9221973310348, (15, 4260): 136.8317546392141, (15, 4262): 139.53509353764207, (15, 4273): 138.8382838152168, (15, 4319): 117.27354293673267, (15, 4326): 116.40933051185877, (15, 4328): 116.55368440554089, (15, 4334): 118.37028567525601, (15, 4335): 117.93658687681834, (15, 4372): 243.87297053085368, (15, 4413): 266.9094661126706, (15, 4434): 241.80353289926546, (15, 4447): 240.224229116955, (15, 4452): 242.6863536043688, (15, 4463): 236.47702023876113, (15, 4465): 235.73900850507175, (15, 4619): 281.1957784515183, (15, 4645): 282.2369102571994, (15, 4657): 283.28563821234144, (15, 4666): 283.50785225002056, (15, 4676): 285.50785626559826, (15, 4678): 285.24451730796886, (15, 4689): 285.6673580044879, (15, 4704): 296.1846465415566, (15, 4726): 353.21349784944164, (15, 4727): 352.29218423882395, (15, 4730): 350.41401642241675, (15, 4731): 351.5565349496158, (15, 4734): 349.11929459583894, (15, 4735): 348.76331151958414, (15, 4736): 349.6539060392629, (15, 4737): 348.71705994395353, (15, 4738): 349.28811250447444, (15, 4756): 350.48591343724246, (15, 4760): 343.3244647588224, (15, 4761): 342.82833472934914, (15, 4762): 342.68338583613166, (15, 4765): 344.0828026801714, (15, 4773): 354.5252034770237, (15, 4774): 354.5231916089911, (15, 4790): 353.7903936897044, (15, 4795): 352.7806384312908, (15, 4799): 355.35531134313123, (15, 4801): 358.40313265114736, (15, 4804): 352.0691982953553, (15, 4805): 351.2513000310092, (15, 4806): 355.3836947634702, (15, 4815): 355.22568969368604, (15, 4816): 357.15441662093474, (15, 4817): 358.55402434217956, (15, 4826): 356.89299585622433, (15, 4830): 355.9920255228414, (15, 4839): 346.0549859832687, (15, 4840): 347.28356973984427, (15, 4841): 345.6746119608869, (15, 4846): 344.8760952707516, (15, 4848): 345.4882996259321, (15, 4850): 346.4639069896974, (15, 4871): 332.0247814882844, (15, 4883): 341.0923701929792, (15, 4900): 335.27307237643447, (15, 4901): 334.7845283656216, (15, 4917): 298.2341478412818, (15, 4931): 292.93684786082554, (15, 4944): 298.178882880561, (15, 4956): 294.5673120598495, (15, 4958): 295.72638505372834, (15, 4959): 295.62878534415256, (15, 4961): 295.10237204686734, (15, 4966): 294.04054079194384, (15, 5207): 288.3810814600848, (15, 5272): 148.19118667832367, (15, 5283): 150.26196495377368, (15, 5287): 157.44875305964828, (15, 5289): 158.50790123170722, (15, 5293): 144.74303795578996, (15, 5295): 150.08298603779, (15, 5296): 152.39092821737574, (15, 5298): 153.6363678251939, (15, 5303): 157.22199569139633, (15, 5305): 151.75809225526447, (15, 5306): 153.73800677453434, (15, 5307): 151.00776111779464, (15, 5308): 153.38790301430578, (15, 5313): 150.29319089348851, (15, 5314): 150.5711652834901, (15, 5317): 154.95999134445316, (15, 5319): 155.95078473374028, (15, 5324): 153.07787329224357, (15, 5326): 151.08864417378734, (15, 5348): 155.3902228668734, (15, 5351): 160.09121686300077, (15, 5399): 163.00506967952725, (15, 5413): 167.6773123159893, (15, 5422): 161.7009376424436, (15, 5445): 158.47312208262218, (15, 5448): 156.7617707651738, (15, 5456): 158.88227030805206, (15, 5467): 161.12625112215954, (15, 5624): 135.1112291936914, (15, 5671): 164.86790106127276, (15, 5672): 161.68383088983265, (15, 5797): 201.73353846441242, (15, 5871): 209.56645905136844, (15, 5976): 189.95737517474956, (15, 6118): 578.535919692425, (15, 6248): 609.5715239741124, (15, 6345): 103.65494094027481, (15, 6352): 110.69953123860499, (15, 6354): 101.63770206098893, (15, 6359): 100.77328589797074, (15, 6376): 110.91666396683983, (15, 6378): 102.5328828801, (15, 6381): 101.72613503047438, (15, 6383): 104.93922639035092, (15, 6396): 104.80294913349319, (15, 6399): 104.21486402432946, (15, 6408): 109.92320272463363, (15, 6409): 105.30242300498665, (15, 6419): 114.78762196882195, (15, 6422): 107.96002817998684, (15, 6423): 108.4566253406116, (15, 6424): 100.8453109870161, (15, 6439): 101.7927295993907, (15, 6464): 103.3595072796677, (15, 6465): 104.47886221072571, (15, 6469): 104.5260771441179, (15, 6470): 105.17814528091377, (15, 6472): 98.5960550347185, (15, 6480): 97.81044744669913, (15, 6486): 91.58368793457993, (15, 6497): 93.53136237175778, (15, 6503): 100.67704531239939, (15, 6508): 101.33081926769643, (15, 6509): 99.43857861700135, (15, 6521): 96.01544630118968, (15, 6544): 95.31325466870254, (15, 6552): 104.61198952354334, (15, 6553): 105.57805558871158, (15, 6554): 106.5771520995648, (15, 6578): 103.17325361302767, (15, 6582): 102.72724860412544, (15, 6601): 102.46515651897144, (15, 6609): 95.86648304133712, (15, 6610): 95.27892991387877, (15, 6611): 95.88090863453293, (15, 6614): 96.89486225334282, (15, 6615): 96.42048164862767, (15, 6616): 94.33186342453496, (15, 6617): 95.15165034020659, (15, 6618): 92.65103708342114, (15, 6619): 97.45125617773238, (15, 6620): 93.83208503143352, (15, 6621): 94.59457883455984, (15, 6622): 94.71969146437696, (15, 6623): 96.42549319664212, (15, 6624): 96.6660063844868, (15, 6625): 97.09149360307116, (15, 6626): 97.72505108819735, (15, 6627): 97.56520305081598, (15, 6628): 93.53970150643352, (15, 6629): 95.84029126521841, (15, 6630): 98.63612521401721, (15, 6632): 96.19118760356982, (15, 6634): 99.22989604076517, (15, 6635): 95.15629459707614, (15, 6636): 94.11629163767707, (15, 6637): 96.96771939950686, (15, 6638): 98.04661762449268, (15, 6639): 97.16816162442676, (15, 6640): 98.1595292816492, (15, 6641): 94.25766724874386, (15, 6642): 97.69497952651533, (15, 6643): 98.19610017219965, (15, 6645): 97.0993462482799, (15, 6646): 93.33201683271828, (15, 6647): 97.62096994848518, (15, 6653): 96.61814052917849, (15, 6655): 97.33005612868462, (15, 6658): 99.0972310623672, (15, 6662): 97.3954302491047, (15, 6819): 142.46110664408465, (15, 6996): 123.31964546445994, (15, 7059): 111.73125686094833, (15, 7187): 137.55448855189096, (15, 7304): 156.54518612360278, (15, 7528): 125.1706969671174, (15, 7720): 55.9255701152698, (15, 7793): 58.521265285385404, (15, 7807): 57.11676494746259, (15, 7808): 59.25564225143077, (15, 7831): 86.53164204877105, (15, 7850): 78.05699486675361, (15, 7852): 81.2390588693735, (15, 8012): 59.13397117592984, (15, 8125): 68.91421125372328, (15, 8208): 35.706233573316304, (15, 8392): 74.27008492544122, (15, 8651): 197.92538288546135, (15, 9088): 153.05453531621654, (15, 9443): 225.37987226226235, (15, 9444): 223.93899840796814, (15, 9828): 280.1552405864444, (15, 9868): 276.9098733117646, (15, 10180): 70.76229499061299, (15, 10256): 62.08875917879472, (15, 10276): 59.11480519625221, (15, 10378): 41.05956761762382, (15, 10676): 99.97950065767678, (15, 10714): 116.27996031058466, (15, 10730): 97.79301665185467, (15, 10862): 285.63573320776817, (15, 10881): 286.0826820521869, (15, 10883): 286.7420616321809, (15, 10885): 285.3689069137467, (15, 10891): 287.7881942285961, (15, 10909): 286.0526360091538, (15, 10911): 284.3746878641571, (15, 10913): 284.8322148356303, (15, 10915): 283.9291804802737, (15, 10919): 283.23733340633163, (15, 11037): 302.8115581758455, (15, 11039): 295.2466772636793, (15, 11516): 280.9251224940264, (15, 11856): 119.0822237176297, (15, 11857): 118.57645688107365, (15, 11861): 118.87062506164287, (15, 11881): 116.97316517893127, (15, 11902): 111.91207933779889, (15, 11911): 110.55845476263508, (15, 11914): 111.44369548442103, (15, 11922): 115.36091264010608, (15, 11924): 116.44336259971259, (15, 11926): 114.95813043112041, (15, 11950): 117.42791217330029, (15, 11963): 122.2638904702932, (15, 11983): 118.48605575998518, (15, 11985): 124.7219435789925, (15, 12009): 123.30792955404276, (15, 12010): 119.98377864266874, (15, 12018): 120.49165966007332, (15, 12020): 121.4817509890376, (15, 12021): 122.00233631640398, (15, 12024): 125.27437650962827, (15, 12025): 124.2568911142589, (15, 12027): 123.45945041048697, (15, 12031): 119.41353793008803, (15, 12032): 120.62232387725771, (15, 12035): 123.00357767081543, (15, 12041): 125.48740430924144, (15, 12045): 79.4292082247961, (15, 12145): 99.99999491786176, (15, 12275): 194.94388942449228, (15, 12294): 188.29032751075607, (15, 12358): 214.92708622731465, (15, 12463): 226.26030289854438, (15, 12465): 226.0617745709861, (15, 12482): 229.01739845048695, (15, 12503): 228.7425990980866, (15, 12506): 229.87825801302455, (15, 12549): 225.91897791313707, (15, 12559): 225.33895575211187, (15, 12569): 226.80273241704023, (15, 12572): 227.62838852206215, (15, 12574): 225.73699709408945, (15, 12576): 226.74107149168017, (15, 12591): 225.73508209068564, (15, 12608): 232.1933850283258, (15, 12696): 220.46283097055843, (15, 12710): 226.1284953222685, (15, 12728): 223.89796172249058, (15, 12766): 71.26847148721527, (15, 12771): 58.78084732669164, (15, 12790): 59.08273373570061, (15, 12795): 61.276604960701704, (15, 12797): 55.03468804948883, (15, 12798): 54.384503814539976, (15, 12811): 54.7438850640644, (15, 12830): 56.55068213200386, (15, 12848): 52.388274354761386, (15, 12850): 49.87411990397949, (15, 12852): 55.245287210546955, (15, 12854): 55.21879525464477, (15, 12859): 51.37451990900982, (15, 12861): 53.33467822601277, (15, 12865): 56.83954771186267, (15, 12866): 55.48245575391256, (15, 12867): 57.03675701240426, (15, 12874): 56.440724958307136, (15, 12875): 56.06843236549066, (15, 12881): 56.964132885789745, (15, 12883): 56.99397506110073, (15, 12885): 56.519837713349595, (15, 12888): 56.07277421593728, (15, 12889): 55.20958146758978, (15, 12892): 56.971890848124396, (15, 12893): 56.94690228124632, (15, 12896): 56.157206475813545, (15, 12906): 60.30604525407609, (15, 13018): 82.39599299918355, (15, 13071): 87.31532406785163, (15, 13131): 69.94323285622355, (15, 13146): 63.81291456834003, (15, 13159): 91.45697825656217, (15, 13193): 69.12533097893505, (15, 13198): 69.45876496536154, (15, 13292): 58.24750854547313, (15, 13296): 48.05891384923472, (15, 13406): 86.6157372003067, (15, 13407): 87.81911675355643, (15, 13417): 95.62425568228339, (15, 13418): 95.81731146352858, (15, 13438): 86.16803140567743, (15, 13442): 82.92789554758197, (15, 13443): 83.9904868111327, (15, 13764): 217.62881774900578, (15, 13766): 216.0322006154243, (15, 13771): 219.5335913825707, (15, 13783): 215.79246117493977, (15, 13784): 213.45506367774314, (15, 13792): 225.54288568960342, (15, 13824): 217.2781517586268, (15, 14017): 197.05845861010403, (15, 14870): 249.28127470538482, (15, 14997): 146.56158054737236, (15, 15000): 146.75395901275664, (15, 15003): 145.98609003436817, (15, 15006): 141.7957492972895, (15, 15007): 140.6490198151557, (15, 15056): 141.8819868161569, (15, 15063): 143.1521089856152, (15, 15069): 144.00149932412842, (15, 15076): 140.70305848667982, (15, 15086): 143.9935755506006, (15, 15087): 145.71405175619947, (15, 15111): 148.95913510390517, (15, 15116): 147.12107135740803, (15, 15722): 178.63279648007386, (15, 15998): 209.08372567470497, (15, 16073): 475.6268101224862, (15, 16939): 620.7942473471991, (15, 16940): 618.9902827537694, (15, 16951): 621.0220128195936, (15, 16963): 621.2006651124873, (15, 16965): 623.4060823151581, (15, 16969): 622.859808396541, (15, 16970): 622.0032421875259, (15, 16971): 620.0168494396402, (15, 16973): 619.8762690335093, (15, 16974): 624.2854365711044, (15, 16976): 622.1621050905853, (15, 16978): 620.7134928717517, (15, 16980): 622.9030540131705, (15, 16982): 624.2624872447008, (15, 17045): 685.264758202069, (15, 17048): 687.8243205894856, (15, 17304): 166.10628919322244, (15, 17305): 165.0511331772619, (15, 17330): 166.18433266797703, (15, 17334): 163.60254637505213, (15, 17343): 168.08236604219718, (15, 17345): 163.7267138550371, (15, 17347): 166.1769636660158, (15, 17351): 160.24633423467378, (15, 17372): 163.40142888943527, (15, 17373): 167.90072399674403, (15, 17377): 168.2366489924337, (15, 17382): 165.35195733346708, (15, 17383): 165.81200726230938, (15, 17389): 164.1280923727692, (15, 17400): 167.02718745151256, (15, 17401): 166.93631246173254, (15, 17402): 167.21873687198226, (15, 17403): 167.5243434526482, (15, 17440): 164.20046976983082, (15, 17455): 167.74929242859127, (15, 17491): 168.24636533826956, (15, 17507): 161.6125602617771, (15, 17509): 163.194531882094, (15, 17590): 159.42052777837577, (15, 17615): 150.29878479287677, (15, 17642): 151.80709992853411, (15, 17643): 151.62069845429414, (15, 17668): 150.2795749865828, (15, 17721): 147.163488304367, (15, 17754): 162.19989844251026, (15, 17769): 162.13300538322449, (15, 17776): 155.83634243728713, (15, 17804): 164.72214768512725, (15, 17809): 166.3185827648153, (15, 17824): 165.31333086745522, (15, 17837): 160.71481494325417, (15, 17838): 160.95415559562585, (15, 17862): 159.80189953397368, (15, 17866): 163.16983973926648, (15, 17872): 158.60604407239683, (15, 17873): 156.04957884974775, (15, 17881): 159.98449203122706, (15, 17947): 473.4643992128154, (15, 17951): 470.03488139405005, (15, 17953): 469.3761768688245, (15, 17954): 469.6141267531645, (15, 17959): 472.7658102990701, (15, 17963): 471.5657497726827, (15, 18000): 454.12355488642487, (15, 18001): 454.80041544989905, (15, 18111): 504.1897703875628, (15, 18148): 416.3605431444637, (15, 18166): 450.5391519131271, (15, 18189): 482.02323226315684, (15, 18239): 168.63062795239927, (15, 18240): 168.62648102977536, (15, 18245): 168.7881669539371, (15, 18247): 168.45361765427165, (15, 18251): 168.80086182513534, (15, 18256): 169.19633080058267, (15, 18258): 168.80367595416075, (15, 18259): 168.88550500210843, (15, 18260): 169.055162986301, (15, 18262): 169.3649967317596, (15, 18263): 169.31155305545732, (15, 18264): 169.4788752121961, (15, 18266): 169.50109038838397, (15, 18267): 169.66345517817015, (15, 18268): 169.75076874300143, (15, 18269): 170.07765640467667, (15, 18275): 169.92340464529735, (15, 18285): 169.41510616100138, (15, 18308): 166.07243398681368, (15, 18313): 164.9823823891928, (15, 18314): 165.50726682583166, (15, 18315): 170.00628513004324, (15, 18316): 170.00565663366461, (15, 18317): 170.15997593695235, (15, 18320): 170.26709886152383, (15, 18321): 170.36355860430913, (15, 18322): 170.6014596182915, (15, 18324): 170.7573030843474, (15, 18325): 171.45973454662294, (15, 18326): 171.19681699842653, (15, 18327): 170.3249049926466, (15, 18329): 171.74647793183678, (15, 18330): 171.47894478006464, (15, 18331): 170.994452946442, (15, 18332): 170.51016143094026, (15, 18333): 171.3805636934899, (15, 18336): 170.94648175512978, (15, 18337): 171.16891522970553, (15, 18403): 170.97189540058005, (15, 18432): 162.69360796559502, (15, 18451): 168.22495292710002, (15, 18466): 173.8888867586307, (15, 18481): 170.12560300440154, (15, 18483): 170.14181642401252, (15, 18484): 169.7432246926022, (15, 18485): 168.53223389380852, (15, 18486): 169.51707681476904, (15, 18487): 168.60753466388107, (15, 18489): 169.45571862710082, (15, 18490): 170.31194333788088, (15, 18491): 170.73348318359317, (15, 18492): 167.71761619627796, (15, 18493): 169.35252655034506, (15, 18494): 169.29626130356567, (15, 18495): 169.99585567678324, (15, 18496): 169.56505554981382, (15, 18497): 168.38793431657908, (15, 18498): 168.64330444842602, (15, 18499): 169.30516656090822, (15, 18501): 168.80281593974024, (15, 18502): 168.37860363924938, (15, 18503): 168.06836364486347, (15, 18504): 169.75695160916857, (15, 18506): 168.83176616345057, (15, 18507): 168.42226673155469, (15, 18508): 169.1996315068144, (15, 18509): 169.1955649150231, (15, 18510): 168.0618335881508, (15, 18511): 169.45599802178245, (15, 18512): 168.97948464078675, (15, 18515): 169.77690176831018, (15, 18516): 169.76776323457167, (15, 18517): 169.21690440136672, (15, 18518): 170.12729752200602, (15, 18519): 169.85709895908147, (15, 18520): 169.09105474918596, (15, 18522): 171.69009206319296, (15, 18523): 171.76288890618346, (15, 18532): 172.3239461017628, (15, 18535): 171.13935498047493, (15, 18537): 170.48003589384885, (15, 18539): 170.60792895341572, (15, 18540): 170.67438674839244, (15, 18541): 170.99085306162493, (15, 18542): 171.19365147381308, (15, 18543): 170.17936026412164, (15, 18546): 170.63089930347223, (15, 18555): 171.66486670196252, (15, 18556): 171.84196783412187, (15, 18565): 172.22277347185923, (15, 18567): 172.49145581326286, (15, 18568): 171.94151917448463, (15, 18577): 175.99614276733317, (15, 18583): 175.36101512611867, (15, 18605): 176.27342506596838, (15, 18608): 172.7809061954966, (15, 18616): 180.04878719489605, (15, 18618): 183.23896478224034, (15, 18625): 182.26889783725406, (15, 18645): 179.50187195860195, (15, 18646): 180.18493881493416, (15, 18653): 177.36077619256932, (15, 18654): 179.94569508089356, (15, 18655): 178.21985001141002, (15, 18666): 188.90146799342833, (15, 18837): 184.0844810831357, (15, 18974): 169.20065435596845, (15, 18999): 172.52759565082667, (15, 19000): 173.48564730677978, (15, 19174): 136.7692691547899, (15, 19342): 157.52177968982804, (15, 19455): 137.15808185778684, (15, 19555): 100.08371891434679, (15, 19564): 108.7193039506479, (15, 19573): 105.7067738202033, (15, 19586): 103.93780481492286, (15, 19605): 103.51562119463512, (15, 19611): 105.30401570385725, (15, 19614): 102.76801777734555, (15, 19641): 125.476248432712, (15, 19702): 126.84454166863004, (15, 19713): 124.80044654120098, (15, 19731): 84.77077231358818, (15, 19819): 132.7497843377059, (15, 19893): 110.33471231795858, (15, 19899): 124.8690229314873, (15, 19929): 112.41870353994605, (15, 19951): 135.57308044061884, (15, 19962): 117.56436829536881, (15, 19970): 116.06324535528948, (15, 19971): 117.64057720458374, (15, 19972): 116.7940553290706, (15, 19975): 114.83691134734111, (15, 19978): 134.325461856331, (15, 19987): 133.84647296359563, (15, 19989): 127.37381617197227, (15, 20039): 134.61423459629634, (15, 20043): 136.13875229020852, (15, 20047): 133.0159298196329, (15, 20052): 126.78552789298682, (15, 20054): 127.92199150601002, (15, 20085): 153.36049348368218, (15, 20104): 155.20423058301407, (15, 20132): 145.03481499781495, (15, 20203): 124.07824193446174, (15, 20280): 126.79165732371456, (15, 20285): 128.35893475640944, (15, 20290): 126.76946443426824, (15, 20297): 124.51677644413375, (15, 20309): 145.6614001800128, (15, 20453): 169.46688666803817, (15, 20485): 111.10977502761277, (15, 20520): 105.4021365204404, (15, 20526): 109.37700053451964, (15, 20698): 294.5168313251587, (15, 20868): 354.26707706150046, (15, 21042): 24.0, (15, 21057): 24.0, (15, 21066): 24.0, (15, 21075): 24.0, (15, 21093): 24.0, (15, 21098): 24.0, (15, 21127): 24.0, (15, 21130): 24.0, (15, 21144): 24.0, (15, 21146): 24.0, (15, 21147): 24.0, (15, 21148): 24.0, (15, 21153): 24.0, (15, 21293): 24.0, (15, 21426): 35.28745152106863, (15, 21442): 50.143867626090554, (15, 21451): 51.49998865591794, (15, 21466): 41.025008670376295, (15, 21469): 41.913571734079156, (15, 21471): 40.67014018498818, (15, 21473): 41.020723965011925, (15, 21475): 40.31917678194, (15, 21482): 43.608789497406306, (15, 21484): 42.83261470416486, (15, 21488): 42.59583280390248, (15, 21494): 38.724696421110075, (15, 21498): 39.79091922720868, (15, 21500): 36.86978708718272, (15, 21514): 34.33069484984794, (15, 21537): 33.177609627765264, (15, 21662): 32.70690494874465, (15, 21691): 26.225245086863747, (15, 21757): 32.345653637149624, (15, 21777): 32.76476271298465, (15, 21778): 34.49868307730159, (15, 21779): 34.55086840481673, (15, 21790): 29.73917213570257, (15, 21802): 31.906963644513027, (15, 21824): 31.45330006219832, (15, 21874): 35.47726134362448, (15, 21879): 38.57651062959591, (15, 21983): 24.0, (15, 22002): 24.0, (15, 22132): 25.829339102119498, (15, 22261): 305.1955488693985, (15, 22298): 301.86961704669386, (15, 22339): 327.95308478108046, (15, 22508): 265.0113380928547, (15, 22841): 718.9634261049812, (15, 22842): 719.0023830913171, (15, 22874): 714.1524273386273, (15, 22941): 714.5607225991342, (15, 22956): 717.6088063443104, (15, 22960): 718.4309375708802, (15, 22968): 721.7945590009307, (15, 22970): 722.5708307137689, (15, 22974): 724.2886067261584, (15, 22980): 727.9223064704229, (15, 23025): 727.860515010654, (15, 23028): 727.1092867296771, (15, 23081): 733.5692831409873, (15, 23104): 727.4646880670006, (15, 23147): 694.5816706324669, (15, 23298): 62.44215355352876, (15, 23376): 56.55052726198004, (15, 23381): 51.703610198159645, (15, 23529): 65.03867631340552, (15, 23556): 61.76113943968339, (15, 23718): 60.79649671015771, (15, 24001): 97.68298777567598, (15, 24094): 106.55994790486248, (15, 24129): 112.39077139294871, (15, 24174): 100.06977359441584, (15, 24235): 112.93707117973166, (15, 24259): 118.49572067353661, (15, 24260): 118.0668979809023, (15, 24261): 116.83421830541812, (15, 24305): 125.17705369069488, (15, 24306): 126.26919563079585, (15, 24307): 124.59406067659998, (15, 24308): 114.46105795778044, (15, 24498): 140.86344760039654, (15, 24499): 140.95644732590006, (15, 24500): 139.91651580269314, (15, 24668): 135.19846851663382, (15, 24711): 147.51034563023453, (15, 24756): 151.1507066271602, (15, 24788): 152.896276351739, (15, 24809): 146.31593321275386, (15, 24813): 148.35254892686137, (15, 24821): 147.68091409744494, (15, 24825): 148.17429272061665, (15, 24832): 145.8731355652591, (15, 24833): 146.86563286577825, (15, 24835): 147.85533323552403, (15, 24837): 149.43869300295594, (15, 24840): 145.7218341254043, (15, 24841): 147.25275931141593, (15, 24844): 145.77119176113862, (15, 24845): 146.66762360541165, (15, 24846): 146.59568468056455, (15, 24849): 147.13767752924429, (15, 24850): 148.6540767604221, (15, 24863): 134.8293169992381, (15, 24866): 136.60143277099309, (15, 24885): 138.7133521775745, (15, 24886): 138.87816852711907, (15, 24889): 142.77664097127737, (15, 24903): 144.32904694585704, (15, 24909): 137.8417854239622, (15, 24999): 218.624319292777, (15, 25019): 217.0953993458492, (15, 25028): 217.38945090263388, (15, 25137): 151.6663916302366, (15, 25145): 152.47184822755275, (15, 25208): 182.37169133800063, (15, 25233): 181.6114722779088, (15, 25371): 138.73190395736881, (15, 25377): 132.14129506198202, (15, 25828): 121.27386681678547, (15, 25851): 120.61648321861637, (15, 25874): 115.33105883242376, (15, 25898): 121.57436822651218, (15, 25946): 121.42829708619466, (15, 26047): 130.68241773821347, (15, 26066): 87.24696971497532, (15, 26197): 105.89196005330865, (15, 26212): 178.0482085965981, (15, 26253): 184.0328462474766, (15, 26254): 181.17251996801255, (15, 26257): 180.9354085801552, (15, 26258): 183.36208692508077, (15, 26260): 181.9728477348416, (15, 26266): 180.0800959087278, (15, 26267): 179.05749900598235, (15, 26271): 179.5157358373584, (15, 26304): 156.71135010855124, (15, 26305): 155.49632288473262, (15, 26363): 134.48588146056858, (15, 26441): 322.9711868044209, (15, 26442): 322.23990607806724, (15, 26450): 319.03614879676894, (15, 26459): 319.0932841844319, (15, 26462): 319.681944228895, (15, 26467): 329.12459698947305, (15, 26471): 326.3195194067741, (15, 26472): 325.9935972078106, (15, 26473): 325.8413044529606, (15, 26476): 323.8977595690363, (15, 26485): 320.5414540242272, (15, 26493): 320.4842401732031, (15, 26524): 321.24273561386195, (15, 26525): 320.7834182308784, (15, 26556): 325.05684636381505, (15, 26560): 325.00828879104466, (15, 26561): 323.03128677529753, (15, 26564): 324.11503988092784, (15, 26569): 322.4453222383093, (15, 26570): 321.53145545571107, (15, 26573): 321.91369427340965, (15, 26581): 321.72330102188533, (15, 26583): 321.08963653857836, (15, 26593): 321.60308866139013, (15, 26837): 329.64730223162456, (15, 26844): 331.85926411537, (15, 26863): 326.77359480015735, (15, 26893): 333.0290952741837, (15, 26902): 336.02175285126344, (15, 26905): 333.22933524177216, (15, 26912): 335.4893061536167, (15, 26921): 329.7860624687307, (15, 26922): 323.43506415197896, (15, 27212): 352.3632523226076, (15, 27218): 350.1483955109474, (15, 27239): 356.4763867479539, (15, 27257): 354.14379768044836, (15, 27274): 357.2466679910071, (15, 27279): 356.6164437876485, (15, 27282): 354.15145164874184, (15, 27283): 355.4400254654078, (15, 27285): 358.26612343248735, (15, 27286): 355.7268602644201, (15, 27290): 352.01785580858626, (15, 27295): 350.7427266410118, (15, 27300): 357.7356899725651, (15, 27344): 350.40996097016006, (15, 27366): 353.0481074643032, (15, 27383): 358.1460956098459, (15, 27398): 361.54346424695285, (15, 27406): 359.20963484786586, (15, 27407): 360.0673610142883, (15, 27426): 357.96537473761333, (15, 27432): 346.96482362681195, (15, 27460): 354.01319009817286, (15, 27523): 351.56409276618086, (15, 27545): 397.93870676097276, (15, 27602): 453.04874510976634, (15, 27606): 454.22211172830725, (15, 27646): 393.376217410318, (15, 27667): 404.5243244236795, (15, 27672): 405.196815724882, (15, 27674): 403.24183343119955, (15, 27688): 405.1840864956382, (15, 27692): 407.02475383901975, (15, 27693): 405.33750499664694, (15, 27705): 405.15088010660884, (15, 27712): 405.897649841473, (15, 27786): 459.24827641144213, (15, 27790): 454.31172002711065, (15, 27791): 453.98316322235377, (15, 27795): 456.0057279113338, (15, 27801): 452.19711750310256, (15, 27813): 460.81820358193266, (15, 27816): 459.04393822007717, (15, 27823): 452.0657565609484, (15, 27830): 456.88434525709135, (15, 27884): 373.7432023745543, (15, 27885): 388.5363802817535, (15, 27896): 379.6465333337783, (15, 27919): 379.13120863371296, (15, 27922): 380.82898007742494, (15, 27930): 376.11508537521735, (15, 27934): 376.5958229240152, (15, 27935): 376.91645652921255, (15, 27948): 443.22469371985846, (15, 27951): 447.5679116621175, (15, 28061): 383.8136607062182, (15, 28290): 503.0758901559039, (15, 28292): 505.19967190641853, (15, 28293): 503.46401073634684, (15, 28295): 502.24208925349717, (15, 28296): 502.84556564674625, (15, 28297): 501.9276851900765, (15, 28302): 500.88359032856647, (15, 28310): 534.6511892015219, (15, 28313): 536.4167797007782, (15, 28372): 536.9090041522677, (15, 28398): 537.0873689887962, (15, 28399): 536.2947990032307, (15, 28400): 537.5577483313132, (15, 28401): 534.265066546358, (15, 28445): 535.2120594633744, (15, 28475): 531.8591006926426, (15, 28885): 113.82632638024351, (15, 28886): 112.87632414151001, (15, 28915): 114.3092153905998, (15, 28916): 113.23901904004983, (15, 28917): 112.79047992079322, (15, 28921): 115.71807111399285, (15, 28931): 115.53675624151099, (15, 28945): 112.53155193426525, (15, 28982): 112.88847792880617, (15, 29219): 124.06473029129285, (15, 29228): 119.29678718484084, (15, 29246): 153.6832805598992, (15, 29248): 154.66983989176728, (15, 29282): 147.81234228486414, (15, 29290): 155.5413523431064, (15, 29291): 154.57827263071914, (15, 29292): 155.66284637005765, (15, 29293): 153.04233241180876, (15, 29294): 155.6786553709358, (15, 29298): 153.583475101246, (15, 29299): 153.7140093987634, (15, 29304): 150.49199280592717, (15, 29317): 143.7583347183159, (15, 29323): 143.19739013040564, (15, 29330): 146.4995410449771, (15, 29331): 147.85493546040124, (15, 29344): 127.3990951751665, (15, 29445): 85.9433572123687, (15, 29724): 708.26400480152, (15, 29738): 709.2370290554081, (15, 29745): 706.3065769429281, (15, 29748): 706.4045104587929, (15, 29750): 707.8012735427933, (15, 29759): 705.1269465004152, (15, 29772): 708.715883972802, (15, 29781): 707.9191039048594, (15, 29784): 707.5026181652312, (15, 29790): 708.619450131542, (15, 29811): 706.3729763284803, (15, 29817): 711.8296469079893, (15, 29818): 711.0468505364711, (15, 29929): 706.2568232767214, (15, 30039): 720.2348019522838, (15, 30066): 712.7960218363412, (15, 30116): 678.6820495223229, (15, 30238): 628.232153231273, (15, 30248): 654.3545572355225, (15, 30260): 655.0340182179457, (15, 30545): 96.14973085591465, (15, 30733): 43.55887233185618, (15, 30756): 34.54859843879638, (15, 30921): 55.91673558311607, (15, 31079): 123.52303764332893, (15, 31149): 114.61241573430964, (15, 31154): 116.532801367238, (15, 31160): 114.58256047869547, (15, 31163): 116.97604519928613, (15, 31189): 126.55726821759384, (15, 31215): 127.42429232772396, (15, 31259): 136.95754693370372, (15, 31262): 137.59275302286483, (15, 31430): 129.52613090171195, (15, 31568): 174.25129814660988, (15, 31751): 133.2288113435546, (16, 109): 207.65263438347617, (16, 872): 311.2757555235269, (16, 873): 313.82075804907964, (16, 877): 313.3495566957804, (16, 879): 313.77414768625675, (16, 884): 312.3103615567289, (16, 889): 313.6706449020761, (16, 891): 311.3380409941237, (16, 892): 315.64641992153963, (16, 894): 315.12726302276593, (16, 896): 311.874785785671, (16, 903): 313.9999059418077, (16, 909): 308.0795831847301, (16, 910): 308.6526036702238, (16, 912): 307.07441412610143, (16, 913): 305.50092370536214, (16, 916): 304.1820349794473, (16, 926): 308.9046068920728, (16, 927): 307.9510268250455, (16, 948): 310.3380436907842, (16, 961): 309.852813900302, (16, 962): 309.8306061276967, (16, 963): 309.9067124335092, (16, 967): 314.8776682540539, (16, 974): 314.65364419473815, (16, 998): 316.2840788723487, (16, 1014): 366.47444706117545, (16, 1086): 292.68080088957163, (16, 1087): 290.94649841235287, (16, 1089): 289.3356013823875, (16, 1090): 290.5244027798465, (16, 1092): 294.1960591279097, (16, 1097): 291.67548936526964, (16, 1107): 295.13584779242655, (16, 1387): 105.50677243339179, (16, 1554): 143.79675607299484, (16, 1827): 437.8342101408576, (16, 1828): 437.890093199554, (16, 1829): 438.42949987914847, (16, 1830): 439.041386477446, (16, 1831): 439.08918627886, (16, 1832): 438.7152643599962, (16, 1833): 438.57144555427556, (16, 1836): 438.0799380261845, (16, 1841): 439.976625407097, (16, 1843): 439.28940638887997, (16, 1844): 439.76862932862724, (16, 1845): 439.10300657431804, (16, 1847): 435.9420496739962, (16, 1848): 436.91697929711285, (16, 1849): 441.658948457136, (16, 1850): 441.9762536336901, (16, 1851): 438.1280328386633, (16, 1852): 438.6023453396301, (16, 1854): 438.74940503562425, (16, 1856): 436.3377646691922, (16, 1857): 437.070588025413, (16, 1858): 440.93574232090253, (16, 1861): 438.71450887821334, (16, 1866): 436.6257190528358, (16, 1867): 439.68459555533616, (16, 1868): 438.80434430936026, (16, 1870): 440.2131250550953, (16, 1871): 439.2218783108715, (16, 1875): 438.4277564948791, (16, 1880): 436.5803866692467, (16, 1882): 437.4413315614931, (16, 1883): 441.5556671863465, (16, 1889): 436.40586125917537, (16, 1893): 437.8256095876834, (16, 1894): 437.0549445177228, (16, 1899): 435.5517905155857, (16, 1900): 435.8985962039978, (16, 1902): 438.9648099084444, (16, 1905): 440.07350054529144, (16, 1907): 437.14435110861825, (16, 1910): 436.96046776710193, (16, 1917): 440.55376756887557, (16, 1920): 436.8537774761072, (16, 1935): 439.42083095448066, (16, 1937): 440.2731243708333, (16, 1946): 433.1884362296379, (16, 1949): 433.7780125481693, (16, 1950): 432.0056398577461, (16, 1951): 433.080912037952, (16, 1952): 435.12557321845526, (16, 1953): 434.5988427390782, (16, 1954): 434.67188339730376, (16, 1958): 433.98504560984645, (16, 1960): 435.5857806251619, (16, 1968): 436.2151009586178, (16, 1969): 438.8122080227387, (16, 1974): 438.201395614378, (16, 1975): 438.4511381842025, (16, 1979): 436.06670789310886, (16, 1980): 436.6993660843307, (16, 1981): 436.75498499624166, (16, 1985): 436.98866471165394, (16, 1994): 432.75648287332956, (16, 2011): 437.6782695876039, (16, 2019): 445.3660643938071, (16, 2020): 444.3554805973135, (16, 2029): 441.29370595344596, (16, 2030): 443.6425446907111, (16, 2032): 441.19570720526855, (16, 2033): 442.42823672891495, (16, 2034): 442.79192091587885, (16, 2036): 441.2409078205952, (16, 2037): 441.57216219246794, (16, 2038): 439.9979068342126, (16, 2042): 450.3953978627821, (16, 2050): 441.3900869844229, (16, 2051): 441.66261807009414, (16, 2053): 441.752866938188, (16, 2054): 442.6870551292304, (16, 2066): 440.8604098120548, (16, 2067): 440.6500244640178, (16, 2071): 430.81840092491956, (16, 2072): 432.2034618839068, (16, 2073): 426.47174999906946, (16, 2074): 426.5089312961899, (16, 2080): 424.32660146199987, (16, 2082): 433.04515765621596, (16, 2083): 433.73664384669786, (16, 2089): 431.59751018263654, (16, 2090): 432.17179194528904, (16, 2092): 430.8369937651133, (16, 2098): 424.874137064629, (16, 2099): 426.0982291985578, (16, 2101): 425.06724942045076, (16, 2102): 429.1425942082208, (16, 2103): 428.01092499496616, (16, 2104): 427.56766902742453, (16, 2106): 434.4835491060051, (16, 2112): 425.9546710622949, (16, 2113): 429.95055230387925, (16, 2114): 431.5743436242993, (16, 2117): 435.42570281098466, (16, 2123): 415.1237983340175, (16, 2124): 415.97561043418517, (16, 2134): 414.4627956604743, (16, 2138): 416.6007788356122, (16, 2141): 414.4757708955611, (16, 2148): 419.30954958115143, (16, 2150): 412.5756719934616, (16, 2151): 413.7320049456574, (16, 2152): 412.34853177817615, (16, 2153): 419.2498344484396, (16, 2154): 415.50785984287614, (16, 2155): 415.71969776030977, (16, 2156): 414.62488769361937, (16, 2157): 417.77956569312687, (16, 2160): 419.5030390445674, (16, 2161): 412.5568125472656, (16, 2162): 420.7789248347718, (16, 2163): 419.4653712837266, (16, 2164): 419.6084637483214, (16, 2168): 414.75887545936297, (16, 2172): 417.2155729643941, (16, 2174): 414.07856662582725, (16, 2178): 418.40275477384785, (16, 2179): 417.9932932368175, (16, 2183): 416.9523756001078, (16, 2185): 417.22547772694554, (16, 2186): 416.42961140263844, (16, 2190): 419.27938851740015, (16, 2192): 417.9223372447104, (16, 2193): 417.06850500514435, (16, 2194): 415.6836238933012, (16, 2195): 415.95434015782183, (16, 2197): 418.450985037251, (16, 2205): 417.1856168835464, (16, 2207): 415.3951299968214, (16, 2208): 416.4911179267843, (16, 2212): 416.4473269592888, (16, 2214): 397.2677373015436, (16, 2225): 401.8584988223486, (16, 2231): 385.21367132345443, (16, 2278): 418.3185792840589, (16, 2284): 421.8845525114341, (16, 2285): 421.8382411829923, (16, 2291): 418.6674157903927, (16, 2292): 416.5336054772503, (16, 2307): 420.1698375927677, (16, 2313): 418.88521415633653, (16, 2317): 413.4175636787164, (16, 2319): 417.74371460469746, (16, 2321): 419.4509991074015, (16, 2323): 418.52371435904683, (16, 2326): 421.9291940651631, (16, 2327): 420.73400037211223, (16, 2329): 419.99588173840453, (16, 2330): 419.3328975767653, (16, 2332): 421.65444302065873, (16, 2344): 417.52569618154257, (16, 2346): 417.99484725741024, (16, 2361): 413.19641411846385, (16, 2368): 429.64049760561846, (16, 2374): 431.3590316356877, (16, 2375): 431.5440250171385, (16, 2377): 426.54033336638497, (16, 2378): 432.599234894552, (16, 2379): 433.23477948475556, (16, 2380): 433.3250858874252, (16, 2383): 427.4629484453032, (16, 2385): 427.999604404264, (16, 2395): 427.6230218677387, (16, 2397): 432.9172503952577, (16, 2398): 425.0036715846665, (16, 2399): 426.44258435961785, (16, 2400): 426.05545178341526, (16, 2402): 430.1685778992972, (16, 2403): 431.2489892929252, (16, 2404): 431.314708506403, (16, 2405): 428.90228925293303, (16, 2407): 430.5596523294392, (16, 2408): 432.04756280611076, (16, 2409): 429.5528137220683, (16, 2411): 432.10658325335726, (16, 2412): 431.49813227637196, (16, 2413): 432.5030584835719, (16, 2414): 431.1806563484701, (16, 2422): 432.0808420753893, (16, 2424): 431.613066546653, (16, 2426): 431.6710584609604, (16, 2433): 430.00412635164406, (16, 2436): 430.0396377305155, (16, 2437): 423.6116926741069, (16, 2440): 424.87281928698405, (16, 2445): 457.26980094421117, (16, 2447): 453.3722728439425, (16, 2454): 456.55554595508096, (16, 2455): 456.31341956234, (16, 2460): 446.99064052910126, (16, 2461): 448.2327884295751, (16, 2471): 470.23914725592283, (16, 2492): 466.71394265143607, (16, 2511): 454.09442204333527, (16, 2523): 460.6116659053386, (16, 2525): 460.1277604752804, (16, 2535): 453.3550077615705, (16, 2537): 451.5045373029319, (16, 2538): 452.3437084045821, (16, 2539): 453.89278886101556, (16, 2540): 454.250046286746, (16, 2542): 456.3456100221259, (16, 2559): 481.57555326317197, (16, 2575): 481.38403730076595, (16, 2599): 430.64823582629, (16, 2600): 442.0838142216877, (16, 2607): 433.8609985141947, (16, 2627): 467.968505609414, (16, 2647): 475.07864975400787, (16, 2674): 469.7560982500075, (16, 2681): 470.17788574796344, (16, 2683): 472.35230326878417, (16, 2686): 468.6573488581482, (16, 2689): 506.0347442803213, (16, 2690): 506.4952047578861, (16, 2713): 522.109732403266, (16, 2714): 523.9043956241069, (16, 2715): 524.7364100016556, (16, 2739): 523.6487861218388, (16, 2740): 515.0972430142914, (16, 2741): 515.2799397512626, (16, 2749): 523.7492660862833, (16, 2750): 523.5880548218222, (16, 2752): 523.9909372750226, (16, 2755): 524.9173083558167, (16, 2758): 525.0794199511611, (16, 2759): 524.8925844171894, (16, 2769): 523.4412124874779, (16, 2771): 517.3041186559053, (16, 2779): 520.6314392822028, (16, 2784): 512.506830173456, (16, 2800): 517.2740286676582, (16, 2802): 515.0999591037422, (16, 2803): 514.3954423069202, (16, 2804): 513.6794125049404, (16, 2805): 516.9713688203427, (16, 2807): 516.5290793781975, (16, 2809): 517.0849238244922, (16, 2812): 510.6761395518555, (16, 2814): 519.3910461819601, (16, 2817): 523.1038247705567, (16, 2819): 515.6876143035818, (16, 2823): 514.5913459884039, (16, 2832): 518.573492920139, (16, 2836): 514.7098251346138, (16, 2839): 516.1222021450378, (16, 2841): 521.5009962795143, (16, 2843): 520.5854675539897, (16, 2846): 517.0505844780814, (16, 2849): 519.8341800907194, (16, 2852): 518.7072450004351, (16, 2853): 520.3769408167935, (16, 2876): 522.5886326592656, (16, 2877): 525.9541926589087, (16, 2885): 530.6161435477618, (16, 2918): 513.6516553131042, (16, 2921): 515.4536884882156, (16, 2925): 505.7563884469211, (16, 2926): 501.81332227349793, (16, 2930): 512.7094448198694, (16, 2931): 507.3963003152079, (16, 2938): 514.3399177312091, (16, 2940): 515.1050206461164, (16, 2947): 509.6601376571148, (16, 2949): 511.1471901457632, (16, 2950): 512.4134535869556, (16, 2952): 511.7674309059181, (16, 2958): 511.36522904210113, (16, 2959): 511.24222783988824, (16, 2960): 512.9815603063229, (16, 2961): 512.5715474220735, (16, 2963): 511.18502133349716, (16, 2968): 512.0024473584045, (16, 2976): 510.6060004120153, (16, 2981): 502.8879018929643, (16, 2982): 503.33914787646813, (16, 2984): 502.88292976911737, (16, 3003): 502.6529224228613, (16, 3046): 485.0441761296442, (16, 3050): 496.0024579028306, (16, 3051): 496.206091780373, (16, 3053): 495.12327709010464, (16, 3069): 504.3892138875047, (16, 3071): 492.9490866540144, (16, 3080): 531.9858044277535, (16, 3199): 505.5649201205144, (16, 3200): 504.6594654213952, (16, 3205): 513.2100816781741, (16, 3209): 505.5163044980813, (16, 3215): 504.2936594031804, (16, 3217): 502.62129104458563, (16, 3249): 503.96672615430873, (16, 3263): 516.4465708778955, (16, 3289): 506.6824627357222, (16, 3301): 508.26309311958744, (16, 3302): 507.2243249847119, (16, 3307): 506.34590733087134, (16, 3310): 508.9868258577105, (16, 3391): 533.6254908371995, (16, 3509): 232.40918232636133, (16, 3510): 231.52140634609705, (16, 3511): 231.26291178163945, (16, 3512): 229.96915153011807, (16, 3514): 229.48259752557297, (16, 3519): 238.6453353874166, (16, 3536): 232.49738251242943, (16, 3545): 233.06386116561393, (16, 3548): 230.5704115110615, (16, 3572): 234.03564734833265, (16, 3581): 235.77034453935303, (16, 3583): 231.6755745535022, (16, 3601): 241.64054053169454, (16, 3656): 243.41956233130426, (16, 3669): 248.70489782716658, (16, 3670): 249.78783531352587, (16, 3695): 242.4002032622697, (16, 3696): 242.88465317690196, (16, 3782): 216.29961132000895, (16, 3792): 217.50672072610305, (16, 3989): 510.52550142328835, (16, 4008): 518.313578108588, (16, 4031): 519.1494417683681, (16, 4045): 515.1079029987613, (16, 4144): 514.2646449082728, (16, 4145): 505.05343460859353, (16, 4164): 510.92924398238756, (16, 4168): 507.84964094893996, (16, 4173): 507.02858163867813, (16, 4181): 502.2820392728911, (16, 4228): 499.2654788575477, (16, 4248): 495.3237417893764, (16, 4254): 446.09200874005916, (16, 4260): 446.97126228407467, (16, 4262): 449.27434520344724, (16, 4273): 449.1325932927335, (16, 4319): 418.8634857479775, (16, 4326): 418.1594116636971, (16, 4328): 418.7230880049085, (16, 4334): 419.7778863577787, (16, 4335): 418.99201655213625, (16, 4372): 319.6647642647213, (16, 4413): 338.86732623905567, (16, 4434): 319.3514525002427, (16, 4447): 323.81202664764277, (16, 4452): 319.372776333774, (16, 4463): 265.4744491576049, (16, 4465): 267.6142232116664, (16, 4619): 336.50337441020395, (16, 4645): 342.45128772597303, (16, 4657): 341.02642549102046, (16, 4666): 338.4651672924291, (16, 4676): 342.12439490704026, (16, 4678): 343.223750852399, (16, 4689): 340.0217286617919, (16, 4704): 358.09561257395467, (16, 4726): 390.2635110023896, (16, 4727): 389.59646662879067, (16, 4730): 388.34174069265356, (16, 4731): 388.45715564468435, (16, 4734): 390.59288086008036, (16, 4735): 389.7504577253553, (16, 4736): 389.88195111024794, (16, 4737): 388.5138978227912, (16, 4738): 388.51337812277916, (16, 4756): 389.0649943081565, (16, 4760): 386.7985638727677, (16, 4761): 387.60426872272876, (16, 4762): 385.6354349920597, (16, 4765): 386.99429128615344, (16, 4773): 391.7814789389139, (16, 4774): 390.8286555176257, (16, 4790): 391.3912615059346, (16, 4795): 390.89834062487495, (16, 4799): 390.9299397468724, (16, 4801): 391.85413094179256, (16, 4804): 391.57600733954666, (16, 4805): 391.1677287708937, (16, 4806): 390.0517510199464, (16, 4815): 389.09893441689644, (16, 4816): 390.940049524605, (16, 4817): 390.8712373806159, (16, 4826): 389.9913543521791, (16, 4830): 388.86481974737296, (16, 4839): 388.6995964168037, (16, 4840): 389.1080623727263, (16, 4841): 387.566440596755, (16, 4846): 387.18025716101596, (16, 4848): 386.6634474054733, (16, 4850): 387.2026666554488, (16, 4871): 381.3121852950797, (16, 4883): 386.59953692154244, (16, 4900): 384.4073798050286, (16, 4901): 383.29103964363964, (16, 4917): 327.92066244352253, (16, 4931): 322.77354342799646, (16, 4944): 328.81049105825844, (16, 4956): 323.40765070223125, (16, 4958): 322.652733490848, (16, 4959): 321.26061127956905, (16, 4961): 324.698107529521, (16, 4966): 321.79748649506104, (16, 5207): 316.0443756588, (16, 5272): 256.87494804158905, (16, 5283): 257.8680940574865, (16, 5287): 257.0231373262068, (16, 5289): 257.39279763062177, (16, 5293): 259.5471174693468, (16, 5295): 262.6781415115504, (16, 5296): 261.1349816905108, (16, 5298): 260.2528005101265, (16, 5303): 259.9321483351838, (16, 5305): 253.23684932956633, (16, 5306): 250.18811087642692, (16, 5307): 252.52715170069973, (16, 5308): 253.253835312302, (16, 5313): 255.14211050748074, (16, 5314): 256.4269970281469, (16, 5317): 252.26542866603805, (16, 5319): 258.44186174293793, (16, 5324): 258.9431871618523, (16, 5326): 259.3659725287671, (16, 5348): 248.60819399196058, (16, 5351): 247.33059841129858, (16, 5399): 255.9030847746521, (16, 5413): 245.55367492444847, (16, 5422): 258.0164339965338, (16, 5445): 254.62413069322704, (16, 5448): 253.4784226379468, (16, 5456): 251.61532422742573, (16, 5467): 252.2687339845598, (16, 5624): 245.79312565069944, (16, 5671): 302.5228276898656, (16, 5672): 301.04592976992933, (16, 5797): 322.6944503151272, (16, 5871): 261.6964393458775, (16, 5976): 244.851325151266, (16, 6118): 415.40118851354094, (16, 6248): 458.19254568604066, (16, 6345): 284.6513394145046, (16, 6352): 282.969514264723, (16, 6354): 284.4681439089321, (16, 6359): 285.91795860752484, (16, 6376): 285.96112463697466, (16, 6378): 284.38200133399005, (16, 6381): 286.53363945436365, (16, 6383): 283.84077006013723, (16, 6396): 290.70321617737886, (16, 6399): 286.0037503054751, (16, 6408): 281.908429244154, (16, 6409): 279.769845244668, (16, 6419): 272.43333994071054, (16, 6422): 279.8081942743542, (16, 6423): 279.5076095532395, (16, 6424): 281.0381398483592, (16, 6439): 279.75170689958117, (16, 6464): 278.33831976474215, (16, 6465): 279.1551836460545, (16, 6469): 281.4920511660814, (16, 6470): 281.8726109265184, (16, 6472): 286.9639744409161, (16, 6480): 281.8001766618199, (16, 6486): 278.0038299017089, (16, 6497): 279.01435256893416, (16, 6503): 272.6716147789871, (16, 6508): 275.92889903174006, (16, 6509): 274.88565978828, (16, 6521): 279.91574229694135, (16, 6544): 276.82193091403275, (16, 6552): 274.92139585205797, (16, 6553): 274.31744673942364, (16, 6554): 273.74568728486327, (16, 6578): 276.37386365341104, (16, 6582): 272.85160739226586, (16, 6601): 275.9805961617194, (16, 6609): 283.47760693148336, (16, 6610): 282.9738750548978, (16, 6611): 284.7629200106895, (16, 6614): 285.5057490063014, (16, 6615): 285.01042761323845, (16, 6616): 283.35548026272465, (16, 6617): 283.89009962698253, (16, 6618): 282.4408260774378, (16, 6619): 284.7973546326036, (16, 6620): 282.32186756158603, (16, 6621): 281.67025251085676, (16, 6622): 282.49700146747324, (16, 6623): 284.3137278124315, (16, 6624): 282.8303635998088, (16, 6625): 283.31612351900736, (16, 6626): 285.2330699654342, (16, 6627): 286.31942285507904, (16, 6628): 281.1674128702985, (16, 6629): 281.66179861583026, (16, 6630): 284.63614813024566, (16, 6632): 282.1999221559363, (16, 6634): 283.50167823941763, (16, 6635): 282.07897009350177, (16, 6636): 283.01805134803465, (16, 6637): 280.9509282784675, (16, 6638): 283.6852232636967, (16, 6639): 285.7498663363109, (16, 6640): 284.28966914047317, (16, 6641): 280.8403528121068, (16, 6642): 282.9940739415237, (16, 6643): 285.934767616986, (16, 6645): 284.3792581033125, (16, 6646): 283.1033849538885, (16, 6647): 283.5123088557619, (16, 6653): 285.314393211595, (16, 6655): 286.0963163234026, (16, 6658): 283.05765186312385, (16, 6662): 282.2168901338599, (16, 6819): 245.47752505152536, (16, 6996): 236.37254258029867, (16, 7059): 242.88468751169472, (16, 7187): 197.33345249935212, (16, 7304): 204.5133980118674, (16, 7528): 220.75359545679393, (16, 7720): 276.2095540204488, (16, 7793): 270.4483184135069, (16, 7807): 272.6594815892093, (16, 7808): 269.115361379357, (16, 7831): 279.665923122028, (16, 7850): 291.0433159793806, (16, 7852): 290.98816752129983, (16, 8012): 280.8439695644841, (16, 8125): 256.27788746089755, (16, 8208): 290.5526313646859, (16, 8392): 269.2542241333649, (16, 8651): 224.5430860668052, (16, 9088): 266.25288582086944, (16, 9443): 153.8216629875656, (16, 9444): 153.23904851894076, (16, 9828): 120.6919434553557, (16, 9868): 148.56627367740177, (16, 10180): 255.24499183806992, (16, 10256): 277.16148551065777, (16, 10276): 270.10391756576655, (16, 10378): 283.95878223996664, (16, 10676): 231.45887848739136, (16, 10714): 211.78402103287328, (16, 10730): 226.87501702575156, (16, 10862): 153.36693980082512, (16, 10881): 158.01500655974914, (16, 10883): 157.42698345533506, (16, 10885): 152.3868710486981, (16, 10891): 156.52361947809112, (16, 10909): 156.2836616168935, (16, 10911): 157.12358099790623, (16, 10913): 155.9889709717507, (16, 10915): 156.04154515787866, (16, 10919): 156.7753448304714, (16, 11037): 124.17701119321829, (16, 11039): 112.49812967183357, (16, 11516): 604.9455353384893, (16, 11856): 420.42921418767116, (16, 11857): 418.1345176755802, (16, 11861): 419.2910708741048, (16, 11881): 419.7823270015166, (16, 11902): 415.1009001933659, (16, 11911): 415.5282573000892, (16, 11914): 415.62069687972036, (16, 11922): 418.6553271107323, (16, 11924): 420.0844053957077, (16, 11926): 418.81096095841446, (16, 11950): 422.8619220561654, (16, 11963): 427.06961434887023, (16, 11983): 426.34916768524073, (16, 11985): 429.07133144030826, (16, 12009): 430.11229493860657, (16, 12010): 426.65501053132635, (16, 12018): 427.4041678969785, (16, 12020): 427.94615433960064, (16, 12021): 428.6510512885408, (16, 12024): 431.52620144858514, (16, 12025): 430.1697561088596, (16, 12027): 429.5836786598363, (16, 12031): 426.1417346826472, (16, 12032): 426.8419044879252, (16, 12035): 430.3551183579635, (16, 12041): 428.3354914759691, (16, 12045): 390.55485608235955, (16, 12145): 410.8081226703965, (16, 12275): 516.7518596278035, (16, 12294): 511.0919170510963, (16, 12358): 537.1648327507501, (16, 12463): 548.656958060878, (16, 12465): 548.5025956660324, (16, 12482): 550.7385599174908, (16, 12503): 550.6338768730517, (16, 12506): 551.6998642898851, (16, 12549): 547.192073543652, (16, 12559): 546.8185637093914, (16, 12569): 548.4725826340541, (16, 12572): 549.2288053017643, (16, 12574): 547.4056694381447, (16, 12576): 547.8525593762324, (16, 12591): 546.3967189763332, (16, 12608): 551.9143177180205, (16, 12696): 540.7636629289685, (16, 12710): 545.1188050987649, (16, 12728): 543.9718637547419, (16, 12766): 371.28213077455325, (16, 12771): 357.4345495676642, (16, 12790): 356.6127635047657, (16, 12795): 355.5061541893141, (16, 12797): 341.51173276581625, (16, 12798): 342.67383659240835, (16, 12811): 351.2608907990911, (16, 12830): 349.5474678663166, (16, 12848): 348.67974292609154, (16, 12850): 347.9907545939163, (16, 12852): 348.4328817572715, (16, 12854): 347.1393981063837, (16, 12859): 349.3568174528485, (16, 12861): 343.57134062310115, (16, 12865): 353.889743740196, (16, 12866): 352.5296040452703, (16, 12867): 355.7529833982425, (16, 12874): 354.28588498727623, (16, 12875): 354.97307201428316, (16, 12881): 351.74451734845627, (16, 12883): 353.26451035232367, (16, 12885): 355.98364505540707, (16, 12888): 352.06481603665867, (16, 12889): 351.2501076026227, (16, 12892): 354.83008766262304, (16, 12893): 352.6005827486609, (16, 12896): 352.88741446174225, (16, 12906): 356.4898157300383, (16, 13018): 358.20123810736385, (16, 13071): 361.302573758174, (16, 13131): 339.8540049652928, (16, 13146): 345.37308405924705, (16, 13159): 350.11201210751415, (16, 13193): 337.4466669914795, (16, 13198): 318.6937134065921, (16, 13292): 333.08930047163545, (16, 13296): 332.519892002234, (16, 13406): 319.261295694796, (16, 13407): 319.5621397731738, (16, 13417): 324.3787827204848, (16, 13418): 326.6818746370991, (16, 13438): 327.74467346616535, (16, 13442): 326.97808135844724, (16, 13443): 326.1366797861425, (16, 13764): 305.27360292176337, (16, 13766): 305.7800655354198, (16, 13771): 308.09705931524803, (16, 13783): 300.1501640167408, (16, 13784): 305.13424483229795, (16, 13792): 311.4020606378676, (16, 13824): 300.3706763900833, (16, 14017): 287.2838178249066, (16, 14870): 160.32731798086607, (16, 14997): 189.41471781100324, (16, 15000): 188.35976573329822, (16, 15003): 187.98702051701454, (16, 15006): 194.87528565291453, (16, 15007): 195.53676386880286, (16, 15056): 191.96097455856417, (16, 15063): 190.56911730228737, (16, 15069): 189.00223547174156, (16, 15076): 194.83301636892375, (16, 15086): 193.8998975425605, (16, 15087): 191.3990047000492, (16, 15111): 190.32565934676884, (16, 15116): 190.80733968869646, (16, 15722): 173.80411108617264, (16, 15998): 127.77610201742525, (16, 16073): 387.1102364295597, (16, 16939): 376.0476147163558, (16, 16940): 374.11932349278146, (16, 16951): 377.95407334534605, (16, 16963): 377.7332408817192, (16, 16965): 379.35841973896396, (16, 16969): 379.81926779885566, (16, 16970): 378.002542899085, (16, 16971): 376.47936258304156, (16, 16973): 376.9702120081087, (16, 16974): 380.57746017286564, (16, 16976): 377.7476235819369, (16, 16978): 376.4265561636313, (16, 16980): 377.8118014858291, (16, 16982): 381.18154108050175, (16, 17045): 480.4335261985463, (16, 17048): 482.7487313172977, (16, 17304): 482.3552785090037, (16, 17305): 482.1790689669919, (16, 17330): 483.01626749021983, (16, 17334): 479.77612993401533, (16, 17343): 485.0191504335795, (16, 17345): 480.7908763337722, (16, 17347): 483.56717565056215, (16, 17351): 476.52965582419915, (16, 17372): 479.9268020729696, (16, 17373): 484.711099365067, (16, 17377): 485.1368741022827, (16, 17382): 482.2543247586871, (16, 17383): 482.4215834763022, (16, 17389): 480.80927060235985, (16, 17400): 483.5636103521928, (16, 17401): 483.3318137689998, (16, 17402): 483.84009302676105, (16, 17403): 484.21656699148275, (16, 17440): 482.1589407556087, (16, 17455): 485.23874211859004, (16, 17491): 486.32371197345014, (16, 17507): 475.49472700169747, (16, 17509): 476.7772787915427, (16, 17590): 476.7162841818904, (16, 17615): 460.9281700350318, (16, 17642): 463.05306447646313, (16, 17643): 463.34332997316466, (16, 17668): 460.59714447976745, (16, 17721): 454.50217593665474, (16, 17754): 468.5630105596533, (16, 17769): 474.75489378723483, (16, 17776): 470.56501184363657, (16, 17804): 477.09160656956703, (16, 17809): 478.6524388422274, (16, 17824): 476.9389072364971, (16, 17837): 475.67679753088555, (16, 17838): 476.4672533251187, (16, 17862): 475.60675254446437, (16, 17866): 478.62377340630877, (16, 17872): 474.11303921077257, (16, 17873): 471.9506794742622, (16, 17881): 475.36182273148165, (16, 17947): 208.02746897460426, (16, 17951): 206.1404419529468, (16, 17953): 205.1180250212636, (16, 17954): 204.81441702437493, (16, 17959): 208.77104905556573, (16, 17963): 209.2695859880889, (16, 18000): 198.33446345466578, (16, 18001): 197.735117480682, (16, 18111): 206.3650623535788, (16, 18148): 137.08850063272325, (16, 18166): 158.81144564146055, (16, 18189): 187.88846996176284, (16, 18239): 485.0888376254745, (16, 18240): 485.1847615814114, (16, 18245): 485.294127630952, (16, 18247): 485.0742829224095, (16, 18251): 485.4276068508023, (16, 18256): 485.94394923683615, (16, 18258): 485.6180081665302, (16, 18259): 485.75026226030593, (16, 18260): 485.9886590382498, (16, 18262): 486.35761662012345, (16, 18263): 486.1119594037705, (16, 18264): 486.3417461402992, (16, 18266): 486.57565119118306, (16, 18267): 486.78435598806044, (16, 18268): 486.92966571262053, (16, 18269): 487.35775066991147, (16, 18275): 487.1563038267243, (16, 18285): 486.2184807880088, (16, 18308): 481.71936518922126, (16, 18313): 480.51710006964333, (16, 18314): 481.4238795002064, (16, 18315): 487.0198636045303, (16, 18316): 487.14121550951427, (16, 18317): 487.35108650695713, (16, 18320): 487.32712386301944, (16, 18321): 487.51154129639633, (16, 18322): 487.81111272948283, (16, 18324): 487.83708134007867, (16, 18325): 488.5564362949626, (16, 18326): 488.28139150247955, (16, 18327): 487.6711276592165, (16, 18329): 488.708848217737, (16, 18330): 488.82458934849, (16, 18331): 488.2680606909386, (16, 18332): 487.77372731245055, (16, 18333): 488.6137195393213, (16, 18336): 487.9814154222519, (16, 18337): 488.1282048326299, (16, 18403): 488.6226086183902, (16, 18432): 483.25336825241743, (16, 18451): 486.9208475261155, (16, 18466): 490.0473756451056, (16, 18481): 486.80052704630384, (16, 18483): 486.9091355224561, (16, 18484): 486.42969997511625, (16, 18485): 484.8745643961116, (16, 18486): 485.54443710308476, (16, 18487): 484.48918591478105, (16, 18489): 485.80707801415866, (16, 18490): 486.4278586494723, (16, 18491): 486.86129756657533, (16, 18492): 483.65550285379175, (16, 18493): 485.2584258472193, (16, 18494): 485.72000038218687, (16, 18495): 486.08832718142196, (16, 18496): 485.7245704575004, (16, 18497): 484.1435922699628, (16, 18498): 484.8058494969562, (16, 18499): 485.5225644920611, (16, 18501): 484.8083069308731, (16, 18502): 484.33690034634884, (16, 18503): 484.11020046521713, (16, 18504): 486.0401183110494, (16, 18506): 484.55789854105484, (16, 18507): 484.0449550094224, (16, 18508): 485.3154151387926, (16, 18509): 485.2195143634875, (16, 18510): 483.9668440586188, (16, 18511): 485.1701497408948, (16, 18512): 484.8404701255612, (16, 18515): 485.92645681273655, (16, 18516): 485.5980635363715, (16, 18517): 484.8434447607599, (16, 18518): 486.07294409954886, (16, 18519): 486.20260644140717, (16, 18520): 485.3125086805036, (16, 18522): 488.34986592908103, (16, 18523): 488.3257845482297, (16, 18532): 488.7747726733171, (16, 18535): 487.718041095079, (16, 18537): 487.1297257992805, (16, 18539): 487.18955982617734, (16, 18540): 487.19120368058543, (16, 18541): 487.4255388020902, (16, 18542): 487.58585795641534, (16, 18543): 486.73996600813786, (16, 18546): 486.9358230298515, (16, 18555): 487.8468667296882, (16, 18556): 487.9298856726084, (16, 18565): 488.543083685277, (16, 18567): 488.5708942863959, (16, 18568): 488.17598038341896, (16, 18577): 491.7947369806803, (16, 18583): 491.5217262330873, (16, 18605): 492.6840299499127, (16, 18608): 488.39389083210284, (16, 18616): 496.04036125971606, (16, 18618): 498.685160048927, (16, 18625): 498.5954931142682, (16, 18645): 496.4250520201172, (16, 18646): 496.79404783899633, (16, 18653): 493.5504850910347, (16, 18654): 495.821774480559, (16, 18655): 494.1458497774373, (16, 18666): 504.96268431254805, (16, 18837): 507.55483745484725, (16, 18974): 489.6746122593655, (16, 18999): 493.5946524291035, (16, 19000): 494.49899553895057, (16, 19174): 460.63714787916837, (16, 19342): 481.46404684571223, (16, 19455): 460.7235181387114, (16, 19555): 422.35234211558566, (16, 19564): 429.6268300003185, (16, 19573): 426.75481097482657, (16, 19586): 425.16611037898605, (16, 19605): 425.11132147847076, (16, 19611): 426.8728673579771, (16, 19614): 424.7914196699819, (16, 19641): 448.55071204581424, (16, 19702): 449.5697027105842, (16, 19713): 447.5335362041562, (16, 19731): 408.26201051072854, (16, 19819): 456.74212643543683, (16, 19893): 343.2989845120331, (16, 19899): 349.5306946920726, (16, 19929): 345.94030817793833, (16, 19951): 362.1542959208927, (16, 19962): 345.2909998659272, (16, 19970): 352.7840606330547, (16, 19971): 351.9394364994908, (16, 19972): 349.9121231770923, (16, 19975): 349.91887211767613, (16, 19978): 369.66306336787466, (16, 19987): 370.5512558301729, (16, 19989): 365.9879011269712, (16, 20039): 371.68865272827884, (16, 20043): 374.4438208887799, (16, 20047): 373.7147236761915, (16, 20052): 367.98584624788754, (16, 20054): 367.9799258448097, (16, 20085): 396.78383832837096, (16, 20104): 398.44464645142887, (16, 20132): 387.47625261136886, (16, 20203): 333.97092834643513, (16, 20280): 329.40946391990144, (16, 20285): 327.8165686221926, (16, 20290): 330.74848777257324, (16, 20297): 329.35522976739236, (16, 20309): 364.6703927911666, (16, 20453): 395.7663629156112, (16, 20485): 320.48550873199946, (16, 20520): 317.23600005035036, (16, 20526): 312.838674679447, (16, 20698): 343.7612927555695, (16, 20868): 350.8852670827437, (16, 21042): 321.2816155759788, (16, 21057): 333.8061466166774, (16, 21066): 326.24638769786134, (16, 21075): 325.9370621841933, (16, 21093): 320.2406556447166, (16, 21098): 326.29979070628855, (16, 21127): 321.25277237561835, (16, 21130): 322.64174768018313, (16, 21144): 324.14915592534277, (16, 21146): 320.44869070941985, (16, 21147): 324.5015497262011, (16, 21148): 326.0028858492279, (16, 21153): 328.28247194041154, (16, 21293): 339.45716458998226, (16, 21426): 354.169132173669, (16, 21442): 370.47767642849834, (16, 21451): 371.96638741732437, (16, 21466): 361.3258911636957, (16, 21469): 362.86261460600144, (16, 21471): 360.5873769065193, (16, 21473): 361.6370287246489, (16, 21475): 360.4557071278905, (16, 21482): 364.5586805352668, (16, 21484): 363.8567699619529, (16, 21488): 363.1523796613634, (16, 21494): 359.43554616786173, (16, 21498): 360.8393963500438, (16, 21500): 357.82092639861577, (16, 21514): 357.67510959668897, (16, 21537): 355.202239768714, (16, 21662): 356.6867182776115, (16, 21691): 349.6747492485801, (16, 21757): 345.0513976294677, (16, 21777): 291.2693663898894, (16, 21778): 289.5240364579757, (16, 21779): 289.5284542037996, (16, 21790): 294.2857558872523, (16, 21802): 292.30255043465496, (16, 21824): 293.1782384079994, (16, 21874): 288.7973849179076, (16, 21879): 285.99759728636764, (16, 21983): 303.15359673714966, (16, 22002): 315.8444164435954, (16, 22132): 326.1958422944542, (16, 22261): 68.83986204319942, (16, 22298): 64.85194894420792, (16, 22339): 55.99325751474101, (16, 22508): 82.08611947778688, (16, 22841): 579.7083211429969, (16, 22842): 579.2542840840099, (16, 22874): 573.3083602217605, (16, 22941): 575.3333386271158, (16, 22956): 577.5939592105964, (16, 22960): 579.4902126070215, (16, 22968): 575.7914626944502, (16, 22970): 577.4344616847418, (16, 22974): 574.7734968958482, (16, 22980): 577.9416505418443, (16, 23025): 571.9096794793508, (16, 23028): 570.0202023455734, (16, 23081): 568.326405218185, (16, 23104): 552.8828248217084, (16, 23147): 541.1453595839833, (16, 23298): 384.0752449825621, (16, 23376): 378.466474982016, (16, 23381): 371.10467500924926, (16, 23529): 384.4223165623566, (16, 23556): 381.6704529783081, (16, 23718): 383.97900735191587, (16, 24001): 418.2269813554605, (16, 24094): 422.37793134693726, (16, 24129): 428.02149708637967, (16, 24174): 413.84137714868797, (16, 24235): 424.7851210969699, (16, 24259): 431.7694254108956, (16, 24260): 431.1234681630197, (16, 24261): 430.1396771685311, (16, 24305): 438.87608337153944, (16, 24306): 439.6489930601395, (16, 24307): 438.188646091801, (16, 24308): 436.37407556568695, (16, 24498): 457.83076342433475, (16, 24499): 457.84151589917764, (16, 24500): 456.922239764437, (16, 24668): 455.9391463732198, (16, 24711): 462.330588696682, (16, 24756): 464.1250064127316, (16, 24788): 466.55712039958627, (16, 24809): 458.36066091003295, (16, 24813): 461.0800810207571, (16, 24821): 460.25973173769063, (16, 24825): 460.5524716971815, (16, 24832): 458.05695435287316, (16, 24833): 459.1262857532869, (16, 24835): 460.0961931641336, (16, 24837): 462.02048209895565, (16, 24840): 457.77670320609604, (16, 24841): 459.66636166307023, (16, 24844): 457.67020689466176, (16, 24845): 459.2506059724631, (16, 24846): 458.30514456724666, (16, 24849): 458.81378692889325, (16, 24850): 461.2173045229449, (16, 24863): 447.47474792168197, (16, 24866): 449.4432249126636, (16, 24885): 451.1878644360307, (16, 24886): 451.0155832829594, (16, 24889): 456.41998889273486, (16, 24903): 458.5729839293984, (16, 24909): 452.41595704906723, (16, 24999): 538.7439675024108, (16, 25019): 537.722309554032, (16, 25028): 537.3528396205103, (16, 25137): 322.765496447767, (16, 25145): 325.05336104235846, (16, 25208): 343.4444085147373, (16, 25233): 340.10519384119476, (16, 25371): 328.67460711169593, (16, 25377): 324.1128949143142, (16, 25828): 219.605984675168, (16, 25851): 210.02038909209924, (16, 25874): 222.40525277783834, (16, 25898): 223.9892835253415, (16, 25946): 218.35941496095504, (16, 26047): 242.5099801256034, (16, 26066): 300.5633852181877, (16, 26197): 266.3241000833111, (16, 26212): 153.8228738252609, (16, 26253): 147.23380837415044, (16, 26254): 150.06734023688207, (16, 26257): 151.35021817169815, (16, 26258): 148.26106998960728, (16, 26260): 149.92451536589078, (16, 26266): 149.8034743222272, (16, 26267): 151.38208659764118, (16, 26271): 151.1508004652338, (16, 26304): 175.3757303214852, (16, 26305): 175.96087117337973, (16, 26363): 208.72187159484358, (16, 26441): 24.0, (16, 26442): 24.0, (16, 26450): 24.0, (16, 26459): 24.0, (16, 26462): 24.0, (16, 26467): 24.0, (16, 26471): 24.0, (16, 26472): 24.0, (16, 26473): 24.0, (16, 26476): 24.0, (16, 26485): 24.0, (16, 26493): 24.0, (16, 26524): 24.0, (16, 26525): 24.0, (16, 26556): 24.0, (16, 26560): 24.0, (16, 26561): 24.0, (16, 26564): 24.0, (16, 26569): 24.0, (16, 26570): 24.0, (16, 26573): 24.0, (16, 26581): 24.0, (16, 26583): 24.0, (16, 26593): 24.0, (16, 26837): 24.0, (16, 26844): 24.0, (16, 26863): 24.0, (16, 26893): 24.0, (16, 26902): 24.0, (16, 26905): 24.0, (16, 26912): 24.0, (16, 26921): 24.0, (16, 26922): 24.0, (16, 27212): 78.97088197468246, (16, 27218): 81.19894676798552, (16, 27239): 79.92374298762364, (16, 27257): 77.9724780264988, (16, 27274): 79.66551463227405, (16, 27279): 78.28100506347974, (16, 27282): 77.35309961547246, (16, 27283): 80.02866112648884, (16, 27285): 79.40266527423385, (16, 27286): 76.44201028315709, (16, 27290): 76.41625761904808, (16, 27295): 77.72260028515217, (16, 27300): 80.29937809521626, (16, 27344): 72.4849387963489, (16, 27366): 72.30668200561306, (16, 27383): 77.02692366535018, (16, 27398): 81.1613853730171, (16, 27406): 80.9767441020215, (16, 27407): 82.21644990188707, (16, 27426): 89.00291062104586, (16, 27432): 83.25387221262228, (16, 27460): 87.84256962442595, (16, 27523): 54.34039995901038, (16, 27545): 100.06701654870496, (16, 27602): 140.88103801028365, (16, 27606): 142.5104063363142, (16, 27646): 79.62207771443695, (16, 27667): 88.86328048596818, (16, 27672): 89.82919626028098, (16, 27674): 87.9287707572671, (16, 27688): 91.18168124627596, (16, 27692): 90.94247728320995, (16, 27693): 89.41823617167698, (16, 27705): 88.82344497905488, (16, 27712): 89.14749721864686, (16, 27786): 163.5550038602332, (16, 27790): 167.08474266622673, (16, 27791): 167.95614795167117, (16, 27795): 160.42684844652106, (16, 27801): 162.254765041177, (16, 27813): 164.0075377070438, (16, 27816): 163.98315331239726, (16, 27823): 162.41077601169587, (16, 27830): 163.94131976017076, (16, 27884): 58.488652406447066, (16, 27885): 74.92172356623946, (16, 27896): 65.3272994941648, (16, 27919): 65.2825106384446, (16, 27922): 66.40973343873341, (16, 27930): 61.787012022881854, (16, 27934): 61.858736592614946, (16, 27935): 61.69806615382315, (16, 27948): 119.66262032555927, (16, 27951): 126.16631816146699, (16, 28061): 118.36145584259285, (16, 28290): 198.7155952912634, (16, 28292): 202.45793943121484, (16, 28293): 199.5646421389371, (16, 28295): 199.6583722506388, (16, 28296): 199.1310351580603, (16, 28297): 196.85138968922766, (16, 28302): 196.95728990588842, (16, 28310): 354.45303676349505, (16, 28313): 359.6402275416843, (16, 28372): 352.7487447690669, (16, 28398): 353.43381091359214, (16, 28399): 353.2759370142158, (16, 28400): 354.4645343615568, (16, 28401): 350.44696049097143, (16, 28445): 360.8980668320335, (16, 28475): 343.0406830616547, (16, 28885): 414.3421069616153, (16, 28886): 412.8451221060086, (16, 28915): 411.95603715224553, (16, 28916): 411.64124563178916, (16, 28917): 410.68289171139514, (16, 28921): 416.68696688622947, (16, 28931): 415.9255293543235, (16, 28945): 404.67887897480466, (16, 28982): 407.9489387405386, (16, 29219): 404.37733927056627, (16, 29228): 400.1385970550641, (16, 29246): 423.3590968798018, (16, 29248): 421.2866492728502, (16, 29282): 416.0155628840581, (16, 29290): 427.8706650687205, (16, 29291): 426.2702278221652, (16, 29292): 427.5271940836405, (16, 29293): 425.38325712278566, (16, 29294): 426.3745043193614, (16, 29298): 425.0994180833662, (16, 29299): 424.46341623415213, (16, 29304): 423.46334634913677, (16, 29317): 418.94036221654324, (16, 29323): 418.64236675775953, (16, 29330): 420.7367563813819, (16, 29331): 422.16159139226795, (16, 29344): 401.3029527722402, (16, 29445): 344.9677793028465, (16, 29724): 590.3305085531761, (16, 29738): 591.1295430573356, (16, 29745): 589.4769888022744, (16, 29748): 593.3769949359395, (16, 29750): 596.1312228392707, (16, 29759): 591.8605049679685, (16, 29772): 594.8667486311, (16, 29781): 594.3088950728185, (16, 29784): 592.3184661644657, (16, 29790): 595.5693497448967, (16, 29811): 595.3853560786325, (16, 29817): 609.9198456341742, (16, 29818): 609.4368698594814, (16, 29929): 587.0552987389578, (16, 30039): 588.0374700553941, (16, 30066): 575.7933677968225, (16, 30116): 555.9476812313698, (16, 30238): 527.0504692682039, (16, 30248): 531.0854499055806, (16, 30260): 530.5355519106361, (16, 30545): 405.0091588057618, (16, 30733): 362.6051121040793, (16, 30756): 340.07065661681844, (16, 30921): 366.25534085548554, (16, 31079): 318.9064914106224, (16, 31149): 302.606604385012, (16, 31154): 304.48888569651587, (16, 31160): 302.03099776185894, (16, 31163): 303.7756339957925, (16, 31189): 281.3127258119041, (16, 31215): 284.3278384781614, (16, 31259): 290.2939900025667, (16, 31262): 287.46717793465336, (16, 31430): 326.12207461730605, (16, 31568): 289.3820473725829, (16, 31751): 312.4994606418165, (17, 109): 387.66786972981305, (17, 872): 205.8766660047801, (17, 873): 207.75211625315603, (17, 877): 206.50519189443966, (17, 879): 206.73238356416493, (17, 884): 203.63358716563317, (17, 889): 205.07343868365567, (17, 891): 203.15349719848368, (17, 892): 208.30892255710478, (17, 894): 208.2891507720014, (17, 896): 207.3813365653796, (17, 903): 205.96249130698928, (17, 909): 204.57392795361213, (17, 910): 205.83473097643514, (17, 912): 204.4915309375617, (17, 913): 202.82187693523935, (17, 916): 202.89179210000796, (17, 926): 207.12701245496916, (17, 927): 206.62581771721332, (17, 948): 202.5588532294479, (17, 961): 205.8450525392606, (17, 962): 206.41623945851597, (17, 963): 206.9425314094283, (17, 967): 206.98009704163658, (17, 974): 204.72248804603683, (17, 998): 207.2957440769295, (17, 1014): 256.41432877843266, (17, 1086): 217.9377658336161, (17, 1087): 219.9426848756085, (17, 1089): 217.22994100627625, (17, 1090): 217.75279104688641, (17, 1092): 220.18091259605245, (17, 1097): 217.88943863240374, (17, 1107): 222.7861882633148, (17, 1387): 270.0195182701257, (17, 1554): 291.9982259444967, (17, 1827): 294.6054773796555, (17, 1828): 294.9594003015975, (17, 1829): 295.23525178724674, (17, 1830): 294.36175632030165, (17, 1831): 294.6573631514522, (17, 1832): 294.45914670349987, (17, 1833): 294.57410267874116, (17, 1836): 294.4086975383458, (17, 1841): 295.74993032366115, (17, 1843): 295.13375227728113, (17, 1844): 295.3221893950178, (17, 1845): 294.5129236711118, (17, 1847): 292.39758973631484, (17, 1848): 293.181531585313, (17, 1849): 296.7823373631884, (17, 1850): 297.24791710723963, (17, 1851): 293.55013433900433, (17, 1852): 293.41053491337067, (17, 1854): 293.9438645645193, (17, 1856): 292.0164072558758, (17, 1857): 293.0169578480914, (17, 1858): 296.5597622713151, (17, 1861): 295.0097459706011, (17, 1866): 291.7925886480706, (17, 1867): 295.9619332156357, (17, 1868): 295.6344661642519, (17, 1870): 295.0002129868384, (17, 1871): 296.0215082085356, (17, 1875): 294.03808998412387, (17, 1880): 292.6928389226814, (17, 1882): 292.6398409420002, (17, 1883): 297.5038191658398, (17, 1889): 293.45162869773134, (17, 1893): 295.61793129605564, (17, 1894): 295.1079254341002, (17, 1899): 293.09172066025394, (17, 1900): 293.5834923056026, (17, 1902): 296.6076817796366, (17, 1905): 297.20904377534663, (17, 1907): 293.9367143699134, (17, 1910): 294.46446471478714, (17, 1917): 299.4395194223661, (17, 1920): 294.1743981543184, (17, 1935): 297.70935638126673, (17, 1937): 298.2675720094676, (17, 1946): 292.3109664124976, (17, 1949): 293.1276622216206, (17, 1950): 290.10151527720006, (17, 1951): 291.44241867229107, (17, 1952): 291.79890135966485, (17, 1953): 292.68921317313004, (17, 1954): 291.75555106517356, (17, 1958): 292.69291576935046, (17, 1960): 293.75940420744473, (17, 1968): 294.18266089067384, (17, 1969): 298.26599446164187, (17, 1974): 297.16023613860364, (17, 1975): 297.012999978991, (17, 1979): 295.5573163827444, (17, 1980): 295.0074598214349, (17, 1981): 295.77211960297797, (17, 1985): 296.3039645064812, (17, 1994): 288.20033165693144, (17, 2011): 292.4792736967034, (17, 2019): 298.04093100419027, (17, 2020): 297.2984070729777, (17, 2029): 294.13830748003244, (17, 2030): 296.7900647242638, (17, 2032): 293.44340171471566, (17, 2033): 295.29613154145716, (17, 2034): 295.09387563946467, (17, 2036): 291.290758526025, (17, 2037): 292.2881017918607, (17, 2038): 293.36406129676317, (17, 2042): 302.4812160101191, (17, 2050): 295.14406277627376, (17, 2051): 294.8209953323598, (17, 2053): 295.1462759730038, (17, 2054): 295.9446104416618, (17, 2066): 294.2867050626177, (17, 2067): 294.3907368914149, (17, 2071): 286.79689988494687, (17, 2072): 288.4582203020755, (17, 2073): 284.8899219769606, (17, 2074): 284.5457793937859, (17, 2080): 281.65757008840666, (17, 2082): 289.3072658151745, (17, 2083): 290.1790119189627, (17, 2089): 288.66504126774015, (17, 2090): 289.5147175549852, (17, 2092): 288.63675289719487, (17, 2098): 282.91192792491705, (17, 2099): 283.6619209524861, (17, 2101): 282.5614263468744, (17, 2102): 286.93933938994337, (17, 2103): 285.4856610232891, (17, 2104): 284.60190532382035, (17, 2106): 290.6301708629495, (17, 2112): 282.96682622919417, (17, 2113): 287.4467490106798, (17, 2114): 288.181981713471, (17, 2117): 291.1294389135803, (17, 2123): 293.7225581449094, (17, 2124): 294.61253712732145, (17, 2134): 291.3744920649337, (17, 2138): 294.27386513640533, (17, 2141): 291.8975679981806, (17, 2148): 290.61246125178474, (17, 2150): 289.6011134216262, (17, 2151): 290.3401207655404, (17, 2152): 288.9246906322981, (17, 2153): 291.15099293917365, (17, 2154): 287.60514684853996, (17, 2155): 286.7551564769813, (17, 2156): 286.36919327180675, (17, 2157): 285.8020787118286, (17, 2160): 294.24705826459535, (17, 2161): 288.50447929717086, (17, 2162): 290.3789677158325, (17, 2163): 289.20208401377397, (17, 2164): 288.9714530594399, (17, 2168): 288.6020893887327, (17, 2172): 288.27483534283397, (17, 2174): 289.8959521616506, (17, 2178): 288.67792033842613, (17, 2179): 288.0068566360619, (17, 2183): 293.9018934337278, (17, 2185): 293.79313644056737, (17, 2186): 293.169199667086, (17, 2190): 294.70574979177866, (17, 2192): 293.5219358024563, (17, 2193): 294.24423993051715, (17, 2194): 293.03893890249765, (17, 2195): 292.5089190051556, (17, 2197): 293.61183627821924, (17, 2205): 291.43077371246966, (17, 2207): 288.70256942042994, (17, 2208): 290.16035813765086, (17, 2212): 295.3839721903079, (17, 2214): 264.73410620488823, (17, 2225): 266.8242163723266, (17, 2231): 268.7668283977884, (17, 2278): 277.50141544329966, (17, 2284): 279.682136952542, (17, 2285): 279.1434306148008, (17, 2291): 272.8161638180104, (17, 2292): 274.75363898519146, (17, 2307): 277.94600003903287, (17, 2313): 271.79464511299767, (17, 2317): 273.4193735667279, (17, 2319): 275.5122267264535, (17, 2321): 276.4816080454331, (17, 2323): 276.7185680246599, (17, 2326): 282.03280079735805, (17, 2327): 280.90675115134985, (17, 2329): 280.09586142879067, (17, 2330): 279.07495925045157, (17, 2332): 280.74056661844406, (17, 2344): 278.4637192355098, (17, 2346): 278.11858012534884, (17, 2361): 280.2765510592895, (17, 2368): 291.8353888756564, (17, 2374): 292.8527859667307, (17, 2375): 293.40975782293896, (17, 2377): 289.3108790678248, (17, 2378): 294.0673794709165, (17, 2379): 293.893606608734, (17, 2380): 294.5199191336392, (17, 2383): 290.6388779253991, (17, 2385): 291.406456819831, (17, 2395): 291.74722712655887, (17, 2397): 293.2538293780407, (17, 2398): 287.97614768545117, (17, 2399): 289.6547639915962, (17, 2400): 289.3157006887399, (17, 2402): 290.94970758979696, (17, 2403): 291.89084340731085, (17, 2404): 292.24932361774063, (17, 2405): 289.8778506400219, (17, 2407): 291.9793045215079, (17, 2408): 292.9620884981964, (17, 2409): 290.6417259175689, (17, 2411): 291.42028708216617, (17, 2412): 291.34516686967254, (17, 2413): 292.05614019679655, (17, 2414): 290.7344829533357, (17, 2422): 290.97347801475934, (17, 2424): 291.7132183060128, (17, 2426): 292.01236596280745, (17, 2433): 290.0687894517386, (17, 2436): 289.29577648954574, (17, 2437): 283.86559124215233, (17, 2440): 285.1449225157281, (17, 2445): 307.69577657514213, (17, 2447): 304.810918060066, (17, 2454): 307.7198294915858, (17, 2455): 308.0531032897948, (17, 2460): 298.80130245314854, (17, 2461): 299.9032699808849, (17, 2471): 317.1370730292923, (17, 2492): 293.66647059937645, (17, 2511): 284.6683653266267, (17, 2523): 289.231549525978, (17, 2525): 287.68360913677265, (17, 2535): 291.9451536473204, (17, 2537): 289.8188719882339, (17, 2538): 291.4081279020386, (17, 2539): 290.2321920326999, (17, 2540): 292.89461427323266, (17, 2542): 294.23058729703297, (17, 2559): 324.84666714817695, (17, 2575): 321.4842614648778, (17, 2599): 279.31931764016446, (17, 2600): 288.5612333946064, (17, 2607): 283.9023043609551, (17, 2627): 289.589901194753, (17, 2647): 295.0997994428202, (17, 2674): 292.3437095294222, (17, 2681): 291.50748418676056, (17, 2683): 294.24754405426626, (17, 2686): 291.1647519848972, (17, 2689): 327.3831325379534, (17, 2690): 327.5584526276314, (17, 2713): 335.11753538027153, (17, 2714): 335.8813472391037, (17, 2715): 336.7751755159836, (17, 2739): 335.93694491218537, (17, 2740): 329.93971832182694, (17, 2741): 330.3645070207624, (17, 2749): 334.8717609871585, (17, 2750): 335.09204514817833, (17, 2752): 335.7034189534907, (17, 2755): 336.4471552806107, (17, 2758): 336.2907655601237, (17, 2759): 336.2669139457385, (17, 2769): 335.1615262127712, (17, 2771): 331.4643099621506, (17, 2779): 332.10496937016615, (17, 2784): 322.2145028075757, (17, 2800): 324.54259372634493, (17, 2802): 328.3674865254928, (17, 2803): 327.9854936561704, (17, 2804): 327.37095277718583, (17, 2805): 329.257893332174, (17, 2807): 329.1545634181529, (17, 2809): 328.92932342895296, (17, 2812): 323.05454156494494, (17, 2814): 329.00282134898697, (17, 2817): 329.83773292017287, (17, 2819): 329.16343912319627, (17, 2823): 324.08035737189476, (17, 2832): 330.4420192818065, (17, 2836): 326.39698078967325, (17, 2839): 329.09550821026545, (17, 2841): 329.6958557506833, (17, 2843): 329.2839496856869, (17, 2846): 327.4150954800845, (17, 2849): 331.16173450036894, (17, 2852): 330.20886998331235, (17, 2853): 331.60397246741985, (17, 2876): 332.28819850440203, (17, 2877): 335.5782207911728, (17, 2885): 337.2550873227116, (17, 2918): 329.3911468284399, (17, 2921): 330.82399002951075, (17, 2925): 324.06503520729524, (17, 2926): 321.8293950315995, (17, 2930): 327.10564093250713, (17, 2931): 324.7180694552272, (17, 2938): 329.46475072703385, (17, 2940): 333.2995900395438, (17, 2947): 328.50157450297667, (17, 2949): 326.93336509318266, (17, 2950): 327.6144483361558, (17, 2952): 326.9269129390583, (17, 2958): 326.7697872557973, (17, 2959): 327.3748409454366, (17, 2960): 328.9285911583586, (17, 2961): 328.2153717256056, (17, 2963): 326.21823448812114, (17, 2968): 326.69196138691484, (17, 2976): 326.00113150307897, (17, 2981): 313.4177852536639, (17, 2982): 313.15500509157965, (17, 2984): 312.5013413541893, (17, 3003): 311.4432331596753, (17, 3046): 301.5789061936401, (17, 3050): 308.8989760762031, (17, 3051): 309.4071746143481, (17, 3053): 307.93809085657495, (17, 3069): 316.48483249530426, (17, 3071): 307.4100172081015, (17, 3080): 337.56720589335157, (17, 3199): 310.16780666908295, (17, 3200): 308.71086504114527, (17, 3205): 318.34863435134383, (17, 3209): 309.5577211451928, (17, 3215): 308.70642863172105, (17, 3217): 306.7886700883349, (17, 3249): 308.7760799739721, (17, 3263): 323.2358325348826, (17, 3289): 313.0913053253717, (17, 3301): 313.7937489138986, (17, 3302): 313.0109695740944, (17, 3307): 312.12263681545426, (17, 3310): 314.62062990388665, (17, 3391): 323.93832610737576, (17, 3509): 24.0, (17, 3510): 24.0, (17, 3511): 24.0, (17, 3512): 24.0, (17, 3514): 24.0, (17, 3519): 24.0, (17, 3536): 24.0, (17, 3545): 24.0, (17, 3548): 24.0, (17, 3572): 24.0, (17, 3581): 24.0, (17, 3583): 24.0, (17, 3601): 24.0, (17, 3656): 24.0, (17, 3669): 24.0, (17, 3670): 24.0, (17, 3695): 24.0, (17, 3696): 24.0, (17, 3782): 24.0, (17, 3792): 24.0, (17, 3989): 592.4714871279774, (17, 4008): 599.5837125035657, (17, 4031): 598.324400564692, (17, 4045): 596.5595891459382, (17, 4144): 597.6923359807101, (17, 4145): 591.3634294993561, (17, 4164): 595.1363199298195, (17, 4168): 593.2964886255721, (17, 4173): 593.0319716216505, (17, 4181): 588.695862771961, (17, 4228): 583.7412421566682, (17, 4248): 583.1220659797507, (17, 4254): 547.783830127294, (17, 4260): 547.5683273825433, (17, 4262): 550.2973771116164, (17, 4273): 549.524340378459, (17, 4319): 527.697703225328, (17, 4326): 526.8431112932236, (17, 4328): 527.0607385649529, (17, 4334): 528.7857317332052, (17, 4335): 528.279900405052, (17, 4372): 518.8607050875196, (17, 4413): 542.0812309407445, (17, 4434): 517.9224554946031, (17, 4447): 521.1179160827594, (17, 4452): 518.2293965107699, (17, 4463): 469.6579273403516, (17, 4465): 471.31909720389217, (17, 4619): 544.347180738814, (17, 4645): 549.6074677847737, (17, 4657): 548.7227224601122, (17, 4666): 546.648089213222, (17, 4676): 550.2721233075025, (17, 4678): 551.113142567917, (17, 4689): 548.5619800177707, (17, 4704): 566.5379664984436, (17, 4726): 607.8968184823269, (17, 4727): 607.1229066875534, (17, 4730): 605.6320297070562, (17, 4731): 605.9945149507697, (17, 4734): 607.2154779166623, (17, 4735): 606.4259735057268, (17, 4736): 606.7463431354995, (17, 4737): 605.3788882593669, (17, 4738): 605.5127467380908, (17, 4756): 606.256232858209, (17, 4760): 602.6572430033523, (17, 4761): 603.2097348119031, (17, 4762): 601.530572612936, (17, 4765): 603.0035290471994, (17, 4773): 609.4756963931004, (17, 4774): 608.6738343034979, (17, 4790): 608.9781044517418, (17, 4795): 608.3300970638738, (17, 4799): 608.9497556590669, (17, 4801): 610.4205093968117, (17, 4804): 608.7331394839254, (17, 4805): 608.1993724563525, (17, 4806): 608.2162784090557, (17, 4815): 607.3767595108696, (17, 4816): 609.3673066967573, (17, 4817): 609.6242579746806, (17, 4826): 608.5074636233584, (17, 4830): 607.3526888260859, (17, 4839): 604.9022359212373, (17, 4840): 605.537104294014, (17, 4841): 603.8635724845416, (17, 4846): 603.3494707439468, (17, 4848): 603.063269261243, (17, 4850): 603.7470063888113, (17, 4871): 595.2993851173968, (17, 4883): 601.9491676408232, (17, 4900): 598.6863620949504, (17, 4901): 597.636479329734, (17, 4917): 541.7439844089388, (17, 4931): 535.9626577544923, (17, 4944): 542.4889755557417, (17, 4956): 536.9329236288082, (17, 4958): 536.5887061328399, (17, 4959): 535.3701177086563, (17, 4961): 538.1761850691511, (17, 4966): 535.4170737637327, (17, 5207): 528.9924314720153, (17, 5272): 425.97653475215395, (17, 5283): 427.96778613360704, (17, 5287): 430.58313851324016, (17, 5289): 431.4390313320105, (17, 5293): 426.91570484142557, (17, 5295): 432.5645678586497, (17, 5296): 432.17108564757586, (17, 5298): 431.9087537690537, (17, 5303): 433.2858273667034, (17, 5305): 424.1259770735759, (17, 5306): 422.0642077130089, (17, 5307): 423.0483952860864, (17, 5308): 424.9421117274258, (17, 5313): 425.29559131068413, (17, 5314): 426.7011863514993, (17, 5317): 424.73031527438394, (17, 5319): 431.2510024602158, (17, 5324): 430.37347257488153, (17, 5326): 429.83206867594095, (17, 5348): 421.30045977299363, (17, 5351): 422.3283387073726, (17, 5399): 432.0942607172896, (17, 5413): 424.1972259622917, (17, 5422): 433.5239764868208, (17, 5445): 428.73462598056733, (17, 5448): 426.79726178270147, (17, 5456): 425.98314957719367, (17, 5467): 427.6913198393374, (17, 5624): 407.67493177073715, (17, 5671): 475.14026513671513, (17, 5672): 472.5391104135275, (17, 5797): 506.5730658112999, (17, 5871): 456.81650989675654, (17, 5976): 433.4629626493858, (17, 6118): 187.573035205112, (17, 6248): 228.2503685599138, (17, 6345): 319.0026321298198, (17, 6352): 312.91558582107336, (17, 6354): 320.3853511714678, (17, 6359): 321.7881039888756, (17, 6376): 314.4121812723284, (17, 6378): 319.6828824763927, (17, 6381): 321.4276657678327, (17, 6383): 317.6280506235443, (17, 6396): 321.58612997603984, (17, 6399): 319.3254018476436, (17, 6408): 312.9241479810343, (17, 6409): 315.2789027488539, (17, 6419): 304.5998010420636, (17, 6422): 313.3071098089952, (17, 6423): 312.7846976207042, (17, 6424): 319.2332162130107, (17, 6439): 317.9028740462457, (17, 6464): 316.0535160774246, (17, 6465): 315.5981462669942, (17, 6469): 316.7169110941942, (17, 6470): 316.42609551672746, (17, 6472): 323.9358069447776, (17, 6480): 321.86616323358146, (17, 6486): 324.8662616130012, (17, 6497): 323.80483933238105, (17, 6503): 315.66655614882416, (17, 6508): 316.5088930624639, (17, 6509): 317.5243073094153, (17, 6521): 322.3252019500278, (17, 6544): 321.5104811582613, (17, 6552): 313.5498461823381, (17, 6553): 312.5426972014351, (17, 6554): 311.52366296227024, (17, 6578): 315.294877616392, (17, 6582): 314.1360161953808, (17, 6601): 315.66200264485417, (17, 6609): 324.1291811433139, (17, 6610): 324.3169788428274, (17, 6611): 324.7630301854394, (17, 6614): 324.4020155293249, (17, 6615): 324.4935627750909, (17, 6616): 325.20442871883756, (17, 6617): 324.86136936088445, (17, 6618): 326.0153849172127, (17, 6619): 323.6282189134858, (17, 6620): 325.07920440674667, (17, 6621): 324.2031265725696, (17, 6622): 324.50194003089024, (17, 6623): 324.1350930952712, (17, 6624): 323.21857447933206, (17, 6625): 323.14362657405974, (17, 6626): 323.6529304760829, (17, 6627): 324.3401783607063, (17, 6628): 324.7595838204364, (17, 6629): 323.2687691370156, (17, 6630): 322.6757282178444, (17, 6632): 323.2646138895964, (17, 6634): 321.65774808092783, (17, 6635): 323.9772277608617, (17, 6636): 325.2006348479545, (17, 6637): 322.08971097290623, (17, 6638): 322.62345997875315, (17, 6639): 324.32962568667176, (17, 6640): 322.84759288963767, (17, 6641): 324.07055625981405, (17, 6642): 322.5371935628668, (17, 6643): 323.67665692776035, (17, 6645): 323.67275630883967, (17, 6646): 325.823591258206, (17, 6647): 322.850497537477, (17, 6653): 324.5052734733197, (17, 6655): 324.39350196142533, (17, 6658): 321.53155879812465, (17, 6662): 322.3772690638013, (17, 6819): 272.02353654535676, (17, 6996): 287.75922171184914, (17, 7059): 299.32378721230975, (17, 7187): 282.7028004698664, (17, 7304): 255.33385967681028, (17, 7528): 287.3543412766066, (17, 7720): 355.50697535048346, (17, 7793): 354.37292182922647, (17, 7807): 355.2097452765051, (17, 7808): 354.1159632270077, (17, 7831): 329.42168392200693, (17, 7850): 340.88882696766626, (17, 7852): 338.5790865131358, (17, 8012): 352.0907037014625, (17, 8125): 364.9736778064893, (17, 8208): 376.7886997518665, (17, 8392): 336.8644258951414, (17, 8651): 216.8929184983622, (17, 9088): 271.68946681033486, (17, 9443): 192.53501857298897, (17, 9444): 194.37659755924003, (17, 9828): 152.5838514939554, (17, 9868): 141.36681134456006, (17, 10180): 366.47849597097735, (17, 10256): 396.5515130017721, (17, 10276): 382.0353749314439, (17, 10378): 384.116502580815, (17, 10676): 360.70212445569484, (17, 10714): 342.66697021675776, (17, 10730): 342.56420223274114, (17, 10862): 379.5153458644142, (17, 10881): 384.11722056543096, (17, 10883): 383.71490330675437, (17, 10885): 378.49838512770555, (17, 10891): 383.1021463506012, (17, 10909): 382.4395966420853, (17, 10911): 382.82325566284186, (17, 10913): 381.84492263037043, (17, 10915): 381.66259096727674, (17, 10919): 382.19140205162756, (17, 11037): 355.0404146000902, (17, 11039): 341.9217281659961, (17, 11516): 660.8394623224805, (17, 11856): 529.5019762624871, (17, 11857): 528.6407175435238, (17, 11861): 529.1161287291812, (17, 11881): 527.5871886799054, (17, 11902): 522.4921443844736, (17, 11911): 521.3573540643112, (17, 11914): 522.1575118207262, (17, 11922): 526.0174859865001, (17, 11924): 527.1638088012583, (17, 11926): 525.6836222597483, (17, 11950): 528.3475513762562, (17, 11963): 533.1753913990308, (17, 11983): 529.5100232395097, (17, 11985): 535.6174830265338, (17, 12009): 534.3262889459302, (17, 12010): 530.989503745571, (17, 12018): 531.5060692980511, (17, 12020): 532.4856970942733, (17, 12021): 533.0138747064035, (17, 12024): 536.2841006848724, (17, 12025): 535.2504138737141, (17, 12027): 534.4583099680672, (17, 12031): 530.4191746854322, (17, 12032): 531.6126464460898, (17, 12035): 534.0274694731194, (17, 12041): 536.2365643532754, (17, 12045): 490.42657460727025, (17, 12145): 511.00495988447483, (17, 12275): 594.0746329878751, (17, 12294): 584.9781549829556, (17, 12358): 611.7239741282021, (17, 12463): 621.8984198483419, (17, 12465): 621.5690882165196, (17, 12482): 626.4161937025938, (17, 12503): 625.7136834669691, (17, 12506): 626.9709929548579, (17, 12549): 624.5444728700453, (17, 12559): 623.5253303874016, (17, 12569): 624.4511653597455, (17, 12572): 625.4027504711531, (17, 12574): 623.4466028047981, (17, 12576): 625.6741096750475, (17, 12591): 625.6225477933266, (17, 12608): 633.401441704944, (17, 12696): 621.2638598544912, (17, 12710): 628.6742792747176, (17, 12728): 624.9184561810865, (17, 12766): 419.4151340439902, (17, 12771): 410.46256935397673, (17, 12790): 409.2005469419897, (17, 12795): 406.25347144971704, (17, 12797): 394.54419559430397, (17, 12798): 396.20257842130667, (17, 12811): 405.7076023745164, (17, 12830): 402.4355064397826, (17, 12848): 404.2733214389966, (17, 12850): 405.19237198285464, (17, 12852): 402.03467414182103, (17, 12854): 400.5743480654192, (17, 12859): 405.7760237913772, (17, 12861): 397.8600663067679, (17, 12865): 407.4251901945552, (17, 12866): 406.7231915179975, (17, 12867): 409.6043608018468, (17, 12874): 408.19961416355574, (17, 12875): 409.3257946899685, (17, 12881): 404.73802083967934, (17, 12883): 406.550137780653, (17, 12885): 410.27369555659266, (17, 12888): 405.7447813588239, (17, 12889): 405.3694327036216, (17, 12892): 408.4944381357695, (17, 12893): 405.7779295521295, (17, 12896): 406.68220156342346, (17, 12906): 408.1618187055622, (17, 13018): 394.7612317805371, (17, 13071): 394.97343308971807, (17, 13131): 383.2299037700748, (17, 13146): 392.9282235520141, (17, 13159): 379.7039876668115, (17, 13193): 381.37688125425757, (17, 13198): 364.6248561752284, (17, 13292): 384.1060146603496, (17, 13296): 389.94986806497377, (17, 13406): 353.97722544901814, (17, 13407): 353.4335653772884, (17, 13417): 352.3315450351551, (17, 13418): 354.19823018316225, (17, 13438): 361.4361774961472, (17, 13442): 362.8635043801622, (17, 13443): 361.44393066704305, (17, 13764): 248.40372988915618, (17, 13766): 250.08790787768893, (17, 13771): 249.36793236644732, (17, 13783): 245.5087281702684, (17, 13784): 251.544161159081, (17, 13792): 247.61151987987506, (17, 13824): 244.52087314504683, (17, 14017): 250.19636383661043, (17, 14870): 374.62624594835904, (17, 14997): 274.7332461453623, (17, 15000): 275.3637145174172, (17, 15003): 277.05824964726463, (17, 15006): 277.8789129967384, (17, 15007): 279.17265742474405, (17, 15056): 280.3135259006103, (17, 15063): 279.4650754321169, (17, 15069): 279.5754532677664, (17, 15076): 279.66967128675327, (17, 15086): 275.20599290725164, (17, 15087): 274.44593299534085, (17, 15111): 270.2685315861361, (17, 15116): 272.70938475920013, (17, 15722): 239.26363908281326, (17, 15998): 232.16824136478422, (17, 16073): 160.8413747066729, (17, 16939): 213.71975915414058, (17, 16940): 212.05004147297856, (17, 16951): 213.35678575028857, (17, 16963): 213.6609115517695, (17, 16965): 215.963667966925, (17, 16969): 215.10535534440274, (17, 16970): 214.60870342819751, (17, 16971): 212.554816986788, (17, 16973): 212.20830811944163, (17, 16974): 216.6890928481145, (17, 16976): 214.9041085042148, (17, 16978): 213.47898888633247, (17, 16980): 215.8508418483879, (17, 16982): 216.46120110987536, (17, 17045): 277.7902319260117, (17, 17048): 280.33348382712825, (17, 17304): 573.7776801226071, (17, 17305): 572.1162025928911, (17, 17330): 573.4336090143896, (17, 17334): 571.4151648096146, (17, 17343): 575.1781091022011, (17, 17345): 570.8939970952929, (17, 17347): 572.9845703987106, (17, 17351): 568.1070657235249, (17, 17372): 570.979947640945, (17, 17373): 575.1004561810943, (17, 17377): 575.3547018964614, (17, 17382): 572.5799790440092, (17, 17383): 573.2400241615389, (17, 17389): 571.567580286195, (17, 17400): 574.4626758695457, (17, 17401): 574.4756607312341, (17, 17402): 574.5852952820328, (17, 17403): 574.827100386427, (17, 17440): 570.5974918823487, (17, 17455): 574.4092782028117, (17, 17491): 574.3580010648601, (17, 17507): 570.7531148317299, (17, 17509): 572.4243289155272, (17, 17590): 566.5786598287111, (17, 17615): 560.7499135959423, (17, 17642): 562.0873748305384, (17, 17643): 561.7780729826228, (17, 17668): 560.7962741723862, (17, 17721): 558.111036616177, (17, 17754): 573.1278979863565, (17, 17769): 571.772497861551, (17, 17776): 564.7435688769493, (17, 17804): 574.3923222773835, (17, 17809): 575.9647473889031, (17, 17824): 575.2201804007511, (17, 17837): 569.3505468534852, (17, 17838): 569.2725729154718, (17, 17862): 567.9842331732734, (17, 17866): 571.4492716447367, (17, 17872): 567.0064410289921, (17, 17873): 564.3031802471602, (17, 17881): 568.4137967659191, (17, 17947): 119.6839608324895, (17, 17951): 116.337963293672, (17, 17953): 116.62152786295158, (17, 17954): 117.45581583005301, (17, 17959): 117.4359663930251, (17, 17963): 114.67946508213085, (17, 18000): 100.77642186215792, (17, 18001): 102.66501987062877, (17, 18111): 185.01718554172643, (17, 18148): 135.01437595870755, (17, 18166): 155.66953447665546, (17, 18189): 168.5084233113839, (17, 18239): 576.0629290871159, (17, 18240): 575.9864438844451, (17, 18245): 576.1801760922667, (17, 18247): 575.7742732650677, (17, 18251): 576.1039789661303, (17, 18256): 576.3941274605888, (17, 18258): 575.9658047206483, (17, 18259): 576.0058566066858, (17, 18260): 576.115733389737, (17, 18262): 576.3671922106123, (17, 18263): 576.464865825787, (17, 18264): 576.5778400999103, (17, 18266): 576.432913160485, (17, 18267): 576.5516707481205, (17, 18268): 576.5885164000952, (17, 18269): 576.8191353905884, (17, 18275): 576.7100617925936, (17, 18285): 576.5621921819181, (17, 18308): 574.1374940900483, (17, 18313): 573.1529874656455, (17, 18314): 573.4210724335708, (17, 18315): 576.9668836138779, (17, 18316): 576.8685067179694, (17, 18317): 576.9714951343788, (17, 18320): 577.1804717239319, (17, 18321): 577.2021729027949, (17, 18322): 577.3802095024348, (17, 18324): 577.6355706109526, (17, 18325): 578.2967168824966, (17, 18326): 578.0539461552432, (17, 18327): 577.0012012614444, (17, 18329): 578.6799539834113, (17, 18330): 578.1091764399044, (17, 18331): 577.704584314414, (17, 18332): 577.248028202125, (17, 18333): 578.1088712565753, (17, 18336): 577.8533218954486, (17, 18337): 578.1272471140833, (17, 18403): 577.3585941907817, (17, 18432): 566.1008150014378, (17, 18451): 573.7186746846631, (17, 18466): 581.343037740117, (17, 18481): 577.3429321618114, (17, 18483): 577.2886651152, (17, 18484): 576.9663299122687, (17, 18485): 576.0505936918318, (17, 18486): 577.2169055142737, (17, 18487): 576.435909194881, (17, 18489): 576.9339632537725, (17, 18490): 577.9234161847241, (17, 18491): 578.3217422293792, (17, 18492): 575.5402268821583, (17, 18493): 577.1390132208095, (17, 18494): 576.7287510640475, (17, 18495): 577.6346124046199, (17, 18496): 577.173294717496, (17, 18497): 576.3053886445745, (17, 18498): 576.2824983236447, (17, 18499): 576.8827867549514, (17, 18501): 576.5425210490832, (17, 18502): 576.1645919870227, (17, 18503): 575.8097287291788, (17, 18504): 577.2723478325023, (17, 18506): 576.7528600050308, (17, 18507): 576.4227152390887, (17, 18508): 576.8508658126515, (17, 18509): 576.9090475994644, (17, 18510): 575.8939550719349, (17, 18511): 577.3633742899375, (17, 18512): 576.8084243465003, (17, 18515): 577.3844013022797, (17, 18516): 577.5893897120762, (17, 18517): 577.1880012050455, (17, 18518): 577.8603519654763, (17, 18519): 577.3248342079147, (17, 18520): 576.6735836459774, (17, 18522): 578.8598348443641, (17, 18523): 579.0024248614483, (17, 18532): 579.6252811605044, (17, 18535): 578.3904405102207, (17, 18537): 577.7029168755736, (17, 18539): 577.8766924327844, (17, 18540): 577.9884369187312, (17, 18541): 578.3530576470012, (17, 18542): 578.5790902260368, (17, 18543): 577.4796605123686, (17, 18546): 578.0992142537599, (17, 18555): 579.1822356817805, (17, 18556): 579.4181929028676, (17, 18565): 579.6222409298173, (17, 18567): 580.0504467673537, (17, 18568): 579.412145286594, (17, 18577): 583.6235371318636, (17, 18583): 582.7609457829551, (17, 18605): 583.4592175289384, (17, 18608): 580.6398777971946, (17, 18616): 587.4023296753398, (17, 18618): 590.8556882382952, (17, 18625): 589.2990599482623, (17, 18645): 586.1673947100965, (17, 18646): 587.0753044851456, (17, 18653): 584.6684269919709, (17, 18654): 587.3836395207302, (17, 18655): 585.683245843173, (17, 18666): 595.8936583136914, (17, 18837): 578.1262025233714, (17, 18974): 572.3774871092531, (17, 18999): 574.5265909528215, (17, 19000): 575.5257197663964, (17, 19174): 525.0326575452142, (17, 19342): 544.5251999990452, (17, 19455): 534.540866799352, (17, 19555): 484.3235361861034, (17, 19564): 486.7416409366624, (17, 19573): 484.71872769396515, (17, 19586): 483.85041919439226, (17, 19605): 484.73090405998494, (17, 19611): 486.11406188161834, (17, 19614): 485.630514069433, (17, 19641): 509.39365983390746, (17, 19702): 508.8215416252184, (17, 19713): 507.1128133345162, (17, 19731): 477.07765266545005, (17, 19819): 526.5493662497039, (17, 19893): 483.67822428998016, (17, 19899): 495.1299839829829, (17, 19929): 486.60634488468645, (17, 19951): 509.1221761420015, (17, 19962): 488.5907712237188, (17, 19970): 493.2496393641518, (17, 19971): 493.4160364356495, (17, 19972): 491.5673270112883, (17, 19975): 490.6301616913014, (17, 19978): 513.6323748957262, (17, 19987): 513.9887595171955, (17, 19989): 507.7944887311873, (17, 20039): 515.1141754328133, (17, 20043): 517.6647764356555, (17, 20047): 515.6518313856545, (17, 20052): 508.83048514822354, (17, 20054): 509.3867565001031, (17, 20085): 540.241343329105, (17, 20104): 542.1763349746464, (17, 20132): 530.3551331160271, (17, 20203): 483.0867788564791, (17, 20280): 480.7570039125685, (17, 20285): 480.20656396290633, (17, 20290): 481.80293428098906, (17, 20297): 479.67411319886384, (17, 20309): 515.5896184122481, (17, 20453): 547.5407119043941, (17, 20485): 466.31654144440813, (17, 20520): 460.92600825337286, (17, 20526): 459.12230753098385, (17, 20698): 226.24991253548686, (17, 20868): 188.26904325054636, (17, 21042): 408.9821292873133, (17, 21057): 421.827384623395, (17, 21066): 415.7198128134674, (17, 21075): 413.0311083220687, (17, 21093): 410.22392553226183, (17, 21098): 419.74936910482984, (17, 21127): 410.1833840365273, (17, 21130): 412.7412956920945, (17, 21144): 412.1194231844059, (17, 21146): 409.34305995391065, (17, 21147): 411.8301173570732, (17, 21148): 414.14832835886875, (17, 21153): 407.94304286683223, (17, 21293): 430.6106370256546, (17, 21426): 425.4956056922943, (17, 21442): 439.0595167360871, (17, 21451): 440.3756089406958, (17, 21466): 432.29649314294335, (17, 21469): 434.3650469896947, (17, 21471): 431.24477088309135, (17, 21473): 432.97002615188177, (17, 21475): 431.44360524421677, (17, 21482): 435.62044758640917, (17, 21484): 435.21662723430194, (17, 21488): 433.99008200777763, (17, 21494): 431.50426846464217, (17, 21498): 433.02730001737876, (17, 21500): 430.677425685526, (17, 21514): 435.11903379754307, (17, 21537): 430.42149916623265, (17, 21662): 437.2047574526746, (17, 21691): 429.1532433236765, (17, 21757): 414.1530312104562, (17, 21777): 385.18436327992384, (17, 21778): 383.1648253207611, (17, 21779): 384.4485291543048, (17, 21790): 387.29523996350406, (17, 21802): 387.48643798673965, (17, 21824): 389.7405454161469, (17, 21874): 385.16807231111164, (17, 21879): 384.28251543453285, (17, 21983): 391.2986642374954, (17, 22002): 414.0260860583832, (17, 22132): 397.7331264541422, (17, 22261): 174.7926639453631, (17, 22298): 180.54014034387595, (17, 22339): 178.66855396793713, (17, 22508): 198.8755427206071, (17, 22841): 349.7723990179126, (17, 22842): 349.4216396574052, (17, 22874): 343.6107015645245, (17, 22941): 345.305394358328, (17, 22956): 347.78974619597625, (17, 22960): 349.47926109273146, (17, 22968): 347.43652312193603, (17, 22970): 348.88566926600134, (17, 22974): 347.3708571137353, (17, 22980): 350.7444442243752, (17, 23025): 346.4296942706801, (17, 23028): 344.87499547485834, (17, 23081): 346.10962151747873, (17, 23104): 334.2463266807688, (17, 23147): 314.11647961804255, (17, 23298): 470.8649861186518, (17, 23376): 465.0936202339818, (17, 23381): 462.1747628435595, (17, 23529): 474.96650899340244, (17, 23556): 471.56402303552534, (17, 23718): 466.92601281063344, (17, 24001): 504.95302948333875, (17, 24094): 516.5016361284718, (17, 24129): 522.2274451324984, (17, 24174): 510.74300698637677, (17, 24235): 523.7309966560715, (17, 24259): 528.9186488880368, (17, 24260): 528.5504131108393, (17, 24261): 527.2835142146085, (17, 24305): 535.3351934067833, (17, 24306): 536.4959436232685, (17, 24307): 534.7968902410875, (17, 24308): 518.6862761927906, (17, 24498): 548.9992472112265, (17, 24499): 549.1429034319724, (17, 24500): 548.0638362282335, (17, 24668): 539.9396582299121, (17, 24711): 556.626143592144, (17, 24756): 560.9255282050692, (17, 24788): 562.3677758027073, (17, 24809): 556.4903812769445, (17, 24813): 558.2765912740127, (17, 24821): 557.6678153952929, (17, 24825): 558.2124715916437, (17, 24832): 556.01746580881, (17, 24833): 556.9669453792752, (17, 24835): 557.9415220860883, (17, 24837): 559.3852709134107, (17, 24840): 555.90554381693, (17, 24841): 557.3001606447311, (17, 24844): 555.9964593728098, (17, 24845): 556.6757796771976, (17, 24846): 556.8550405792919, (17, 24849): 557.3953022866373, (17, 24850): 558.6241732560625, (17, 24863): 545.075287177537, (17, 24866): 546.7538958985342, (17, 24885): 548.9250755625286, (17, 24886): 549.1768249846413, (17, 24889): 552.5186049173831, (17, 24903): 553.7943213805373, (17, 24909): 547.3532611255522, (17, 24999): 619.8209862406087, (17, 25019): 617.4813683882657, (17, 25028): 618.8993772303595, (17, 25137): 486.4447565868225, (17, 25145): 488.643099601405, (17, 25208): 515.6474037844555, (17, 25233): 512.7288091899405, (17, 25371): 485.5470732854927, (17, 25377): 478.9470741438684, (17, 25828): 364.8084616504769, (17, 25851): 346.32780001162786, (17, 25874): 363.115957983167, (17, 25898): 371.73157841213015, (17, 25946): 362.9689717967419, (17, 26047): 401.47463759758506, (17, 26066): 437.3462715498558, (17, 26197): 413.0564941990053, (17, 26212): 315.9538057056987, (17, 26253): 311.3410301990058, (17, 26254): 312.82369891042373, (17, 26257): 315.2985106112663, (17, 26258): 312.51583129837314, (17, 26260): 313.8809314232592, (17, 26266): 310.14907462819497, (17, 26267): 312.07953942903356, (17, 26271): 312.3765190472048, (17, 26304): 328.32270912370353, (17, 26305): 327.6172139078667, (17, 26363): 360.9129140908726, (17, 26441): 229.99511143487143, (17, 26442): 229.2388564382207, (17, 26450): 230.3538718739516, (17, 26459): 234.33567600265536, (17, 26462): 235.90977210172417, (17, 26467): 233.56836269232147, (17, 26471): 232.19258081744786, (17, 26472): 231.6773518922967, (17, 26473): 231.1399058897904, (17, 26476): 225.7229700162202, (17, 26485): 231.95618155548993, (17, 26493): 229.91625627374276, (17, 26524): 237.2812786587647, (17, 26525): 236.3078115643398, (17, 26556): 232.69815043240706, (17, 26560): 236.0627262234964, (17, 26561): 237.32876250152765, (17, 26564): 232.02043638096472, (17, 26569): 236.37422075267492, (17, 26570): 235.33649786751033, (17, 26573): 233.4556339992575, (17, 26581): 231.92353150938567, (17, 26583): 233.07284427087097, (17, 26593): 229.95339395632837, (17, 26837): 231.82113378361416, (17, 26844): 232.07393536615086, (17, 26863): 227.72334280220068, (17, 26893): 226.79818651725324, (17, 26902): 227.03282508391644, (17, 26905): 230.25555625196918, (17, 26912): 229.3458069864145, (17, 26921): 227.49726658888935, (17, 26922): 221.81256077060172, (17, 27212): 310.3131384879456, (17, 27218): 313.2798320623776, (17, 27239): 310.15233798515857, (17, 27257): 308.7045832052575, (17, 27274): 309.6098520665409, (17, 27279): 308.26069115747697, (17, 27282): 308.0150174002801, (17, 27283): 310.5939587393093, (17, 27285): 308.96274200771796, (17, 27286): 306.48894679484556, (17, 27290): 307.61000621821563, (17, 27295): 309.38007183018453, (17, 27300): 310.1609369636446, (17, 27344): 303.7557959652623, (17, 27366): 302.74417904744837, (17, 27383): 306.29627140765876, (17, 27398): 309.77030771976456, (17, 27406): 310.4211610563091, (17, 27407): 311.53088232281067, (17, 27426): 319.80593159627375, (17, 27432): 316.1169917184207, (17, 27460): 319.5516611205017, (17, 27523): 282.6905238318617, (17, 27545): 312.4249279484265, (17, 27602): 319.2556244682219, (17, 27606): 321.1658197215577, (17, 27646): 281.5665731335602, (17, 27667): 282.8083699766046, (17, 27672): 283.87820291908133, (17, 27674): 283.0183947404795, (17, 27688): 287.1354251713295, (17, 27692): 282.997277903198, (17, 27693): 282.56690735224123, (17, 27705): 281.42398062503634, (17, 27712): 280.6779304006875, (17, 27786): 358.4439956816622, (17, 27790): 369.3999955720239, (17, 27791): 371.1028961626335, (17, 27795): 356.31038321149464, (17, 27801): 363.32703828055145, (17, 27813): 357.51606959108625, (17, 27816): 359.445952697564, (17, 27823): 363.71000753949073, (17, 27830): 361.6420635901142, (17, 27884): 268.90021186999246, (17, 27885): 279.40162956913355, (17, 27896): 273.5656111887107, (17, 27919): 274.247950084811, (17, 27922): 273.93593416871204, (17, 27930): 271.84646273337466, (17, 27934): 271.26828292860256, (17, 27935): 270.4475682638519, (17, 27948): 266.81909686217807, (17, 27951): 284.5446830108786, (17, 28061): 127.2636396664918, (17, 28290): 198.2727775969423, (17, 28292): 195.68825505106787, (17, 28293): 197.4184178835597, (17, 28295): 193.9424142845536, (17, 28296): 196.71383346290392, (17, 28297): 199.36898233485832, (17, 28302): 196.2726823651368, (17, 28310): 131.34608064708073, (17, 28313): 134.9956282986089, (17, 28372): 131.85477139888718, (17, 28398): 132.26846195517692, (17, 28399): 131.72389338048367, (17, 28400): 133.01757030791197, (17, 28401): 129.22772337262944, (17, 28445): 135.11305079290983, (17, 28475): 124.66800211883346, (17, 28885): 523.9654983132904, (17, 28886): 522.8731452928125, (17, 28915): 523.796632510571, (17, 28916): 522.8809194961759, (17, 28917): 522.2885283018918, (17, 28921): 525.9943444957418, (17, 28931): 525.6941360849955, (17, 28945): 520.2804951519124, (17, 28982): 521.5963473442487, (17, 29219): 527.8472449360644, (17, 29228): 522.9668326236564, (17, 29246): 554.7171405212512, (17, 29248): 554.3258108213374, (17, 29282): 547.7306267417887, (17, 29290): 557.8980106897352, (17, 29291): 556.5905011766856, (17, 29292): 557.8208299738942, (17, 29293): 555.2466797487649, (17, 29294): 557.3125947170904, (17, 29298): 555.4525204933176, (17, 29299): 555.2438016613561, (17, 29304): 552.8138552895492, (17, 29317): 546.6235362144547, (17, 29323): 546.1418488535066, (17, 29330): 549.1255923928601, (17, 29331): 550.5991858016856, (17, 29344): 528.4740323549978, (17, 29445): 472.78336364507584, (17, 29724): 357.02300583532934, (17, 29738): 357.8500899599316, (17, 29745): 356.0439756575316, (17, 29748): 359.6301950828333, (17, 29750): 362.299012412621, (17, 29759): 358.1199273413527, (17, 29772): 361.2045278118315, (17, 29781): 360.62041835009114, (17, 29784): 358.7535345500053, (17, 29790): 361.8443917544697, (17, 29811): 361.4951840462706, (17, 29817): 375.6231785746256, (17, 29818): 375.12789888414125, (17, 29929): 353.8505176711744, (17, 30039): 356.7971716605143, (17, 30066): 345.2893123096636, (17, 30116): 322.76128406650787, (17, 30238): 292.67692229886063, (17, 30248): 297.6287098461286, (17, 30260): 297.2081325763366, (17, 30545): 507.13593896416296, (17, 30733): 454.3861074955159, (17, 30756): 441.30970315959905, (17, 30921): 466.3382856162633, (17, 31079): 328.95058785015055, (17, 31149): 322.4601534298566, (17, 31154): 322.4768823933299, (17, 31160): 322.07273559174314, (17, 31163): 321.65000180069933, (17, 31189): 300.22069075151995, (17, 31215): 301.3266638929999, (17, 31259): 298.0379120996632, (17, 31262): 295.7363795021221, (17, 31430): 331.04976518211816, (17, 31568): 269.4492797800894, (17, 31751): 316.9683747628258, (25, 109): 150.38858912948078, (25, 872): 528.5859083848666, (25, 873): 531.0294252445515, (25, 877): 530.1046472311343, (25, 879): 530.4664604530396, (25, 884): 527.994570949827, (25, 889): 529.5299640348253, (25, 891): 527.1874546242656, (25, 892): 532.3627074139675, (25, 894): 532.0572494482152, (25, 896): 529.7170088055625, (25, 903): 530.187992985934, (25, 909): 526.0550813759278, (25, 910): 527.0426691772454, (25, 912): 525.4248798478056, (25, 913): 523.6387076082817, (25, 916): 522.8975637447112, (25, 926): 527.8569430864663, (25, 927): 527.0392667809961, (25, 948): 526.3025042290715, (25, 961): 527.7468169853357, (25, 962): 528.0305185422708, (25, 963): 528.3474632764319, (25, 967): 531.2243880855832, (25, 974): 529.8974304724462, (25, 998): 532.1861951034836, (25, 1014): 585.6900021360647, (25, 1086): 523.0248091975437, (25, 1087): 522.7933068990394, (25, 1089): 520.5052913811975, (25, 1090): 521.5260833072507, (25, 1092): 525.0379937904734, (25, 1097): 522.3446227094382, (25, 1107): 526.8333841386141, (25, 1387): 167.41559048320855, (25, 1554): 130.99257902160315, (25, 1827): 640.4528759802726, (25, 1828): 640.7126264186778, (25, 1829): 641.0906918182452, (25, 1830): 640.7083810500659, (25, 1831): 640.9275424643181, (25, 1832): 640.6620890927944, (25, 1833): 640.6905240115206, (25, 1836): 640.4056826836282, (25, 1841): 641.9832534453942, (25, 1843): 641.3230331686327, (25, 1844): 641.6182780514556, (25, 1845): 640.8333481484201, (25, 1847): 638.2851782709334, (25, 1848): 639.1617297333806, (25, 1849): 643.2718300058505, (25, 1850): 643.7008611670407, (25, 1851): 639.8360451513101, (25, 1852): 639.9036454714686, (25, 1854): 640.320837272798, (25, 1856): 638.1643477270356, (25, 1857): 639.1034345903764, (25, 1858): 642.8700650218341, (25, 1861): 641.0376500671822, (25, 1866): 638.1111828037966, (25, 1867): 642.026287394432, (25, 1868): 641.4940838713102, (25, 1870): 641.5499058020866, (25, 1871): 641.9042542753501, (25, 1875): 640.2741339503682, (25, 1880): 638.7107295605845, (25, 1882): 638.9743555260521, (25, 1883): 643.7311883839875, (25, 1889): 639.1643148013109, (25, 1893): 641.1345184429854, (25, 1894): 640.5141091283149, (25, 1899): 638.616059060397, (25, 1900): 639.0719910503524, (25, 1902): 642.2098602195701, (25, 1905): 643.0109246763125, (25, 1907): 639.755079517454, (25, 1910): 640.0467139419256, (25, 1917): 644.6859966420595, (25, 1920): 639.8127064583242, (25, 1935): 643.1155620457744, (25, 1937): 643.7974398584842, (25, 1946): 637.2339679015809, (25, 1949): 637.9948127163727, (25, 1950): 635.3249549546792, (25, 1951): 636.6146138668329, (25, 1952): 637.5899142903539, (25, 1953): 638.0017965072581, (25, 1954): 637.3991245391309, (25, 1958): 637.7809667056371, (25, 1960): 639.0774826622043, (25, 1968): 639.589181838397, (25, 1969): 643.2670746599252, (25, 1974): 642.3056760981068, (25, 1975): 642.2977921029675, (25, 1979): 640.4546980567948, (25, 1980): 640.3181930948294, (25, 1981): 640.8503403749198, (25, 1985): 641.2907457339701, (25, 1994): 634.3066705870418, (25, 2011): 638.9456869867428, (25, 2019): 645.388277649533, (25, 2020): 644.5361249169115, (25, 2029): 641.315086778519, (25, 2030): 643.9452997458062, (25, 2032): 640.7960144126938, (25, 2033): 642.4996335174823, (25, 2034): 642.4773377279521, (25, 2036): 639.2873546413175, (25, 2037): 640.1020979505239, (25, 2038): 640.3440962579157, (25, 2042): 650.1453796563377, (25, 2050): 642.048056803779, (25, 2051): 641.9141521547751, (25, 2053): 642.1709479322617, (25, 2054): 643.0383268467951, (25, 2066): 641.2745460049126, (25, 2067): 641.2763744834504, (25, 2071): 632.6687152764152, (25, 2072): 634.2875250175564, (25, 2073): 629.8146748467886, (25, 2074): 629.5986244564376, (25, 2080): 626.8665492527037, (25, 2082): 635.1620732102631, (25, 2083): 635.9987294870949, (25, 2089): 634.2114239249895, (25, 2090): 634.9907270571714, (25, 2092): 633.9179163602741, (25, 2098): 627.906567772382, (25, 2099): 628.8567555181234, (25, 2101): 627.7428493083407, (25, 2102): 632.1633588430959, (25, 2103): 630.7764890461139, (25, 2104): 630.0216809876827, (25, 2106): 636.5691881830958, (25, 2112): 628.3377606498153, (25, 2113): 632.7972978121941, (25, 2114): 633.8766471470406, (25, 2117): 637.2400926943538, (25, 2123): 630.5840651083502, (25, 2124): 631.495693295254, (25, 2134): 628.9059787597108, (25, 2138): 631.5849460193341, (25, 2141): 629.2192818170753, (25, 2148): 630.5970732019435, (25, 2150): 627.0020970868787, (25, 2151): 627.9641229097049, (25, 2152): 626.500412925093, (25, 2153): 630.899587217111, (25, 2154): 627.1193342561185, (25, 2155): 626.6937338276458, (25, 2156): 625.9843129392209, (25, 2157): 626.980276306857, (25, 2160): 632.8778613361407, (25, 2161): 626.3468402148944, (25, 2162): 631.0805571865624, (25, 2163): 629.7979000917319, (25, 2164): 629.7159950741832, (25, 2168): 627.3915756576991, (25, 2172): 628.2670798251437, (25, 2174): 627.8586339377216, (25, 2178): 629.0231252990777, (25, 2179): 628.4358518083934, (25, 2183): 631.5266596679661, (25, 2185): 631.5864025601895, (25, 2186): 630.857481363035, (25, 2190): 633.0517192158035, (25, 2192): 631.7398563854671, (25, 2193): 631.7809731957817, (25, 2194): 630.4412425843208, (25, 2195): 630.2523866189292, (25, 2197): 632.0299974433983, (25, 2205): 630.1635691548514, (25, 2207): 627.7332308336358, (25, 2208): 629.0938286281028, (25, 2212): 632.1626299368647, (25, 2214): 605.226702136583, (25, 2225): 608.4648690774368, (25, 2231): 602.029409842499, (25, 2278): 621.871007428646, (25, 2284): 624.649193362162, (25, 2285): 624.2719266760929, (25, 2291): 618.8527612697097, (25, 2292): 619.3814087419582, (25, 2307): 622.8576686621684, (25, 2313): 618.2282561438518, (25, 2317): 617.3197039985689, (25, 2319): 620.3367359232955, (25, 2321): 621.6140589577692, (25, 2323): 621.4294632799581, (25, 2326): 626.2233031800968, (25, 2327): 625.02897671255, (25, 2329): 624.2153611309981, (25, 2330): 623.2921233140877, (25, 2332): 625.2672074495339, (25, 2344): 622.1995956057857, (25, 2346): 622.1541266245741, (25, 2361): 621.6193022141383, (25, 2368): 635.584980156493, (25, 2374): 636.9070055742253, (25, 2375): 637.3418441176813, (25, 2377): 632.7455572577453, (25, 2378): 638.1741159197077, (25, 2379): 638.2998678865526, (25, 2380): 638.7460103431338, (25, 2383): 633.9644756364472, (25, 2385): 634.670035348538, (25, 2395): 634.7413789625564, (25, 2397): 637.7587108393982, (25, 2398): 631.2824156438869, (25, 2399): 632.9297812989329, (25, 2400): 632.5592871838259, (25, 2402): 635.2068180129169, (25, 2403): 636.2336541057264, (25, 2404): 636.4942930742444, (25, 2405): 634.0232038956407, (25, 2407): 636.0307631591127, (25, 2408): 637.2396582230951, (25, 2409): 634.7713211068701, (25, 2411): 636.2422715816334, (25, 2412): 635.9666343313874, (25, 2413): 636.811412242964, (25, 2414): 635.4438057782934, (25, 2422): 635.935329754297, (25, 2424): 636.2530343801252, (25, 2426): 636.4723441191453, (25, 2433): 634.5643464427038, (25, 2436): 634.0654894697358, (25, 2437): 628.0667731548313, (25, 2440): 629.3860450332581, (25, 2445): 656.0210161824809, (25, 2447): 652.7447219000953, (25, 2454): 655.8170854335577, (25, 2455): 655.9786741700171, (25, 2460): 646.4507516350614, (25, 2461): 647.6286731102258, (25, 2471): 666.7220914211164, (25, 2492): 647.0446445739227, (25, 2511): 637.3715390182389, (25, 2523): 642.3186725274815, (25, 2525): 640.9095074529312, (25, 2535): 643.1283866693309, (25, 2537): 641.0234187480412, (25, 2538): 642.4677285203901, (25, 2539): 641.8930759792172, (25, 2540): 644.0843638568624, (25, 2542): 645.6228335426495, (25, 2559): 675.5445947562138, (25, 2575): 672.8735743360895, (25, 2599): 627.3989810773959, (25, 2600): 637.5713708020152, (25, 2607): 631.6848386194845, (25, 2627): 643.507091437782, (25, 2647): 649.1590988122232, (25, 2674): 646.1972714598809, (25, 2681): 645.4597776669075, (25, 2683): 648.172597623651, (25, 2686): 645.0170358487464, (25, 2689): 681.495511407198, (25, 2690): 681.6838269242625, (25, 2713): 689.1424721355022, (25, 2714): 689.8225083307376, (25, 2715): 690.716881938938, (25, 2739): 689.9037767176139, (25, 2740): 684.0820029650021, (25, 2741): 684.5148365481692, (25, 2749): 688.7402314195268, (25, 2750): 688.9954857310096, (25, 2752): 689.6223638455889, (25, 2755): 690.3452143174559, (25, 2758): 690.1593454124117, (25, 2759): 690.1513748355134, (25, 2769): 689.0841761443032, (25, 2771): 685.571923812258, (25, 2779): 686.0226322924667, (25, 2784): 676.019617742119, (25, 2800): 678.0126017185444, (25, 2802): 682.4370869914393, (25, 2803): 682.0750106524215, (25, 2804): 681.4680864864986, (25, 2805): 683.2574961806303, (25, 2807): 683.1792204747857, (25, 2809): 682.8959832142114, (25, 2812): 677.0894339826317, (25, 2814): 682.7486928389952, (25, 2817): 683.1709276859724, (25, 2819): 683.2422517829369, (25, 2823): 677.8479315587471, (25, 2832): 684.4027734589976, (25, 2836): 680.3640506666214, (25, 2839): 683.1438503038523, (25, 2841): 683.2542818066594, (25, 2843): 682.9143997076661, (25, 2846): 681.2544264328654, (25, 2849): 685.0715433838539, (25, 2852): 684.1396577039773, (25, 2853): 685.5019332756742, (25, 2876): 686.0203641035338, (25, 2877): 689.276968843803, (25, 2885): 690.4959930574142, (25, 2918): 683.5638364593067, (25, 2921): 684.9830881695974, (25, 2925): 678.2583926978187, (25, 2926): 675.979734181007, (25, 2930): 681.2372481791391, (25, 2931): 678.9167505612129, (25, 2938): 683.6185724485357, (25, 2940): 687.4981084278204, (25, 2947): 682.6918748029364, (25, 2949): 681.1112377635206, (25, 2950): 681.7748461085022, (25, 2952): 681.0874292450304, (25, 2958): 680.9380247884554, (25, 2959): 681.55948985618, (25, 2960): 683.1071476021507, (25, 2961): 682.3875718298192, (25, 2963): 680.3761638815935, (25, 2968): 680.8365292768754, (25, 2976): 680.1705366918065, (25, 2981): 667.3593838547147, (25, 2982): 667.0324950068948, (25, 2984): 666.3636530749977, (25, 3003): 665.2251700309058, (25, 3046): 655.7741690683494, (25, 3050): 663.0185398160972, (25, 3051): 663.5388334395096, (25, 3053): 662.0569719797586, (25, 3069): 670.5299931393025, (25, 3071): 661.5881914885184, (25, 3080): 690.6090521750219, (25, 3199): 663.3442360494963, (25, 3200): 661.8009099280786, (25, 3205): 671.5275071119269, (25, 3209): 662.6351984318553, (25, 3215): 661.8651819410584, (25, 3217): 659.9248314457542, (25, 3249): 662.0065062840266, (25, 3263): 676.6442596620269, (25, 3289): 666.541578419199, (25, 3301): 667.0935573004444, (25, 3302): 666.3624216039193, (25, 3307): 665.4819727810951, (25, 3310): 667.9289744500171, (25, 3391): 671.6931023312385, (25, 3509): 351.78935684328565, (25, 3510): 350.39572577199084, (25, 3511): 351.2889009019053, (25, 3512): 350.39693122990775, (25, 3514): 350.6634470727409, (25, 3519): 355.24341014037907, (25, 3536): 354.1869819751658, (25, 3545): 356.34016464013763, (25, 3548): 354.16100889347223, (25, 3572): 355.02012693954197, (25, 3581): 353.4538653376707, (25, 3583): 352.35589952016744, (25, 3601): 357.92426823813264, (25, 3656): 355.83037583301945, (25, 3669): 353.5202755407058, (25, 3670): 354.7889025957275, (25, 3695): 347.465972254713, (25, 3696): 348.4458672602753, (25, 3782): 354.2613523187147, (25, 3792): 352.7730313775431, (25, 3989): 248.23461537793227, (25, 4008): 255.8700052952865, (25, 4031): 255.77612328766116, (25, 4045): 252.6816225267728, (25, 4144): 252.772641424585, (25, 4145): 244.85017958400894, (25, 4164): 249.75653482910877, (25, 4168): 247.24924710367992, (25, 4173): 246.70411061269073, (25, 4181): 242.07465233608943, (25, 4228): 237.97531421299644, (25, 4248): 235.723474644927, (25, 4254): 194.84913305045845, (25, 4260): 194.878129042456, (25, 4262): 197.55451212047538, (25, 4273): 196.91755812716556, (25, 4319): 173.5611416350505, (25, 4326): 172.71003856693693, (25, 4328): 172.9480881541391, (25, 4334): 174.64573618363895, (25, 4335): 174.1249045219784, (25, 4372): 250.2013791908813, (25, 4413): 275.0898683935425, (25, 4434): 248.29692043250114, (25, 4447): 248.0383651739824, (25, 4452): 249.081091822944, (25, 4463): 229.86548722571032, (25, 4465): 229.7220767558151, (25, 4619): 287.00404339790134, (25, 4645): 289.28310701714133, (25, 4657): 289.8689145114049, (25, 4666): 289.4745981840316, (25, 4676): 292.05740559610905, (25, 4678): 292.07973029656614, (25, 4689): 291.7156250500155, (25, 4704): 304.95116934847806, (25, 4726): 361.01354972725954, (25, 4727): 360.0840101880046, (25, 4730): 358.2101884656948, (25, 4731): 359.21532142535926, (25, 4734): 357.5688984616897, (25, 4735): 357.0873267894073, (25, 4736): 357.8790593655436, (25, 4737): 356.7891344266585, (25, 4738): 357.27928432027306, (25, 4756): 358.42270544023347, (25, 4760): 351.7996515739157, (25, 4761): 351.5434514749088, (25, 4762): 351.0042593429577, (25, 4765): 352.49191574092055, (25, 4773): 362.45447484523726, (25, 4774): 362.25500947502303, (25, 4790): 361.7429620810627, (25, 4795): 360.7740475682371, (25, 4799): 362.9902075587814, (25, 4801): 365.7972729798705, (25, 4804): 360.30469603465133, (25, 4805): 359.5179624201498, (25, 4806): 362.8326092926567, (25, 4815): 362.49957318617595, (25, 4816): 364.5365945269402, (25, 4817): 365.72393978668623, (25, 4826): 364.11603429956955, (25, 4830): 363.10931272109747, (25, 4839): 354.543017438626, (25, 4840): 355.68302824965104, (25, 4841): 353.9787475974638, (25, 4846): 353.2121012480522, (25, 4848): 353.62930358071634, (25, 4850): 354.5801711522824, (25, 4871): 340.9304230246267, (25, 4883): 349.84143303757054, (25, 4900): 344.38067884424777, (25, 4901): 343.7234748837952, (25, 4917): 300.00029532817234, (25, 4931): 294.197366524449, (25, 4944): 300.1483646398182, (25, 4956): 295.77486596057, (25, 4958): 296.62876071141926, (25, 4959): 296.2347350898751, (25, 4961): 296.53244955669953, (25, 4966): 294.95317313383805, (25, 5207): 288.67209530918217, (25, 5272): 142.588952667759, (25, 5283): 145.07295949327215, (25, 5287): 151.9340100164016, (25, 5289): 153.1260794547767, (25, 5293): 140.19634754736913, (25, 5295): 146.7911437016188, (25, 5296): 148.47721952113113, (25, 5298): 149.37248434398802, (25, 5303): 152.80217382171182, (25, 5305): 144.74988534782457, (25, 5306): 145.56497357153197, (25, 5307): 143.7040391299586, (25, 5308): 146.41007709658246, (25, 5313): 144.0209300745618, (25, 5314): 144.81282386064703, (25, 5317): 147.6182301511222, (25, 5319): 150.97976410728987, (25, 5324): 148.3117552586948, (25, 5326): 146.4916059081123, (25, 5348): 146.63695516216526, (25, 5351): 150.9469684309739, (25, 5399): 157.03994913994896, (25, 5413): 157.98847737335933, (25, 5422): 156.51884818244096, (25, 5445): 152.05470839234147, (25, 5448): 149.90370899252147, (25, 5456): 151.33453040723126, (25, 5467): 153.83511640599014, (25, 5624): 124.08003294718208, (25, 5671): 175.0917936694109, (25, 5672): 171.72770397022106, (25, 5797): 213.96622629811455, (25, 5871): 203.7224808406618, (25, 5976): 179.9271763418528, (25, 6118): 525.107037508515, (25, 6248): 557.519431200755, (25, 6345): 66.64036205173512, (25, 6352): 72.6486430196188, (25, 6354): 64.57393337542112, (25, 6359): 64.54165152981697, (25, 6376): 74.33260089886379, (25, 6378): 65.40058130104434, (25, 6381): 65.80358571778903, (25, 6383): 67.46067288188402, (25, 6396): 70.99472451030262, (25, 6399): 67.90972044921062, (25, 6408): 71.36490540232411, (25, 6409): 65.68787511807042, (25, 6419): 71.82247297091374, (25, 6422): 68.37186033552823, (25, 6423): 68.71868968778014, (25, 6424): 61.89224492371623, (25, 6439): 62.14048906190044, (25, 6464): 62.97167952279091, (25, 6465): 64.53755538033302, (25, 6469): 65.81309180420482, (25, 6470): 66.66026846840549, (25, 6472): 63.04077588686647, (25, 6480): 59.2804387457567, (25, 6486): 50.599231200265784, (25, 6497): 53.2622303330895, (25, 6503): 57.148779700146754, (25, 6508): 59.59361890648235, (25, 6509): 57.04001500225774, (25, 6521): 56.361385682209985, (25, 6544): 53.80100238123106, (25, 6552): 62.477717546060724, (25, 6553): 63.17539353220372, (25, 6554): 63.92988217043516, (25, 6578): 61.74216392911106, (25, 6582): 59.42681495705762, (25, 6601): 60.80066996755634, (25, 6609): 58.329661194893845, (25, 6610): 57.4437739838226, (25, 6611): 59.112712436225465, (25, 6614): 60.54439446482256, (25, 6615): 59.78834019565047, (25, 6616): 56.73277388397129, (25, 6617): 57.8701415747306, (25, 6618): 54.48694923602928, (25, 6619): 60.67026086207662, (25, 6620): 55.59999803864339, (25, 6621): 55.969716318899, (25, 6622): 56.59705858100099, (25, 6623): 59.37936593416544, (25, 6624): 58.73941268170475, (25, 6625): 59.447730320876886, (25, 6626): 61.19229557480742, (25, 6627): 61.67296295132649, (25, 6628): 54.594329733258284, (25, 6629): 57.220213704628044, (25, 6630): 61.73544499514009, (25, 6632): 57.892418790823506, (25, 6634): 61.668790908234584, (25, 6635): 56.782237082373584, (25, 6636): 56.3116544425072, (25, 6637): 57.93810071784991, (25, 6638): 60.60709715033389, (25, 6639): 60.95393533228886, (25, 6640): 61.06839826377442, (25, 6641): 55.12392146290775, (25, 6642): 59.8579861542642, (25, 6643): 62.05841657012668, (25, 6645): 60.08007542902195, (25, 6646): 55.58175626014061, (25, 6647): 60.08636046362717, (25, 6653): 60.161705318869195, (25, 6655): 61.31469319611347, (25, 6658): 61.28459861021765, (25, 6662): 59.10716913495355, (25, 6819): 91.53927688016194, (25, 6996): 68.1284609657813, (25, 7059): 56.715938065857166, (25, 7187): 79.395431152999, (25, 7304): 98.953959930841, (25, 7528): 67.14249485276133, (25, 7720): 24.0, (25, 7793): 24.0, (25, 7807): 24.0, (25, 7808): 24.0, (25, 7831): 46.38217048436716, (25, 7850): 46.4551000765402, (25, 7852): 49.32571860795819, (25, 8012): 24.0, (25, 8125): 36.23976490325487, (25, 8208): 24.0, (25, 8392): 24.0, (25, 8651): 144.79255896616837, (25, 9088): 108.29674928771693, (25, 9443): 166.99598169281236, (25, 9444): 165.53092650935068, (25, 9828): 221.66455755768965, (25, 9868): 218.70429597967333, (25, 10180): 39.964179628892275, (25, 10256): 60.03279589418853, (25, 10276): 44.3617017919746, (25, 10378): 33.65849989721696, (25, 10676): 67.69490592762013, (25, 10714): 75.73161943562069, (25, 10730): 53.55868145207038, (25, 10862): 252.7012304692586, (25, 10881): 253.9817288496353, (25, 10883): 254.52138925820964, (25, 10885): 252.26192795685347, (25, 10891): 255.38337156440906, (25, 10909): 253.6380740000616, (25, 10911): 252.1428324632101, (25, 10913): 252.38574325627815, (25, 10915): 251.50719368311394, (25, 10919): 250.96061096927065, (25, 11037): 264.6818428663613, (25, 11039): 255.34635094212393, (25, 11516): 335.8465650462382, (25, 11856): 175.362160405897, (25, 11857): 174.4499712486752, (25, 11861): 174.9439691150922, (25, 11881): 173.51259383854523, (25, 11902): 168.41233004682422, (25, 11911): 167.40164186158262, (25, 11914): 168.14249748943868, (25, 11922): 171.96473829101038, (25, 11924): 173.14280268215074, (25, 11926): 171.66845169093997, (25, 11950): 174.50054383556576, (25, 11963): 179.30639178237388, (25, 11983): 176.0104358440582, (25, 11985): 181.72334139448105, (25, 12009): 180.72396485615138, (25, 12010): 177.32622810629843, (25, 12018): 177.88402755325583, (25, 12020): 178.8114911034065, (25, 12021): 179.37218636845446, (25, 12024): 182.62544380914986, (25, 12025): 181.53356478714318, (25, 12027): 180.76063547532556, (25, 12031): 176.7569859869433, (25, 12032): 177.89505361097363, (25, 12035): 180.50682713361306, (25, 12041): 182.21649670086947, (25, 12045): 136.86693517753042, (25, 12145): 157.75131516870144, (25, 12275): 252.5399236256563, (25, 12294): 245.42221180866727, (25, 12358): 272.2641783225272, (25, 12463): 283.4785967664845, (25, 12465): 283.25754147670875, (25, 12482): 286.527425941968, (25, 12503): 286.185985460665, (25, 12506): 287.34623506126974, (25, 12549): 283.59578272117, (25, 12559): 282.948729208764, (25, 12569): 284.3392760027348, (25, 12572): 285.1879488128749, (25, 12574): 283.2774090693944, (25, 12576): 284.4656494867482, (25, 12591): 283.58807445632397, (25, 12608): 290.2371140954877, (25, 12696): 278.4178135810473, (25, 12710): 284.30921169914086, (25, 12728): 281.892785940733, (25, 12766): 103.05060295991417, (25, 12771): 88.64409771425433, (25, 12790): 88.03227157773823, (25, 12795): 87.69662851504859, (25, 12797): 74.31268723216651, (25, 12798): 75.10811651686492, (25, 12811): 82.49005347599808, (25, 12830): 81.49476230333818, (25, 12848): 79.73810968304264, (25, 12850): 78.60669331978845, (25, 12852): 80.21585515972394, (25, 12854): 79.1166784933963, (25, 12859): 80.10703448250301, (25, 12861): 75.58358257397104, (25, 12865): 85.21061584625359, (25, 12866): 83.7405977264653, (25, 12867): 86.82649921581866, (25, 12874): 85.45045145937628, (25, 12875): 85.94764956218008, (25, 12881): 83.44156943575227, (25, 12883): 84.72280238685143, (25, 12885): 86.90540423711779, (25, 12888): 83.48828048045924, (25, 12889): 82.59099504676695, (25, 12892): 86.03348987019292, (25, 12893): 84.15430836948711, (25, 12896): 84.20272097064536, (25, 12906): 88.24042751323341, (25, 13018): 97.49555374914023, (25, 13071): 101.86677390958606, (25, 13131): 78.61045678714004, (25, 13146): 80.38911004190537, (25, 13159): 96.60323213382004, (25, 13193): 76.40373232575881, (25, 13198): 62.00440278784799, (25, 13292): 68.32624362161437, (25, 13296): 64.48963726599027, (25, 13406): 73.45418255533794, (25, 13407): 74.48995305286576, (25, 13417): 83.0207672643268, (25, 13418): 84.56971162499444, (25, 13438): 78.83568495370531, (25, 13442): 76.2747805151533, (25, 13443): 76.36489441579012, (25, 13764): 179.45927234075944, (25, 13766): 178.11903284650543, (25, 13771): 181.85188751712954, (25, 13783): 176.59633030568475, (25, 13784): 175.6137605490539, (25, 13792): 188.07556523081365, (25, 13824): 178.01397004606588, (25, 14017): 156.18906796578798, (25, 14870): 217.61083557617468, (25, 14997): 88.40349729542636, (25, 15000): 88.69956274208069, (25, 15003): 88.08004738191556, (25, 15006): 83.50899057175981, (25, 15007): 82.39201206498572, (25, 15056): 83.93182645617489, (25, 15063): 85.24103718307659, (25, 15069): 86.22637380954204, (25, 15076): 82.51292979054777, (25, 15086): 85.63828048712202, (25, 15087): 87.4365180495731, (25, 15111): 90.56868763406757, (25, 15116): 88.79642379094233, (25, 15722): 120.14219192998061, (25, 15998): 151.80177017975026, (25, 16073): 427.24768444757956, (25, 16939): 562.9237974892688, (25, 16940): 561.1096590469385, (25, 16951): 563.2106198358639, (25, 16963): 563.3758114541965, (25, 16965): 565.5684285837735, (25, 16969): 565.0557677771793, (25, 16970): 564.1624953517486, (25, 16971): 562.1854799964894, (25, 16973): 562.0666118190699, (25, 16974): 566.462657842824, (25, 16976): 564.307572166632, (25, 16978): 562.8585087096869, (25, 16980): 565.0278039991099, (25, 16982): 566.4618642732112, (25, 17045): 629.7505917425212, (25, 17048): 632.3099336188383, (25, 17304): 224.59733373150874, (25, 17305): 223.51927350207475, (25, 17330): 224.66180704845232, (25, 17334): 222.09564817600486, (25, 17343): 226.55439155631322, (25, 17345): 222.19877909364905, (25, 17347): 224.63203812713945, (25, 17351): 218.7394476855701, (25, 17372): 221.88908702213755, (25, 17373): 226.37725255594373, (25, 17377): 226.70981674399647, (25, 17382): 223.82796470170518, (25, 17383): 224.2960558241261, (25, 17389): 222.61164851427344, (25, 17400): 225.51210163305453, (25, 17401): 225.42434569276713, (25, 17402): 225.70138543041756, (25, 17403): 226.00479992811, (25, 17440): 222.62558324502186, (25, 17455): 226.19702290574685, (25, 17491): 226.65541257294691, (25, 17507): 220.06794924539142, (25, 17509): 221.6401170031496, (25, 17590): 217.88861464356563, (25, 17615): 208.48587810403797, (25, 17642): 210.05952878026613, (25, 17643): 209.91318777850014, (25, 17668): 208.43543000173347, (25, 17721): 204.94152141941993, (25, 17754): 219.9823545278705, (25, 17769): 220.52612224046814, (25, 17776): 214.31290298281488, (25, 17804): 223.10698163734796, (25, 17809): 224.7056078667197, (25, 17824): 223.65042788694225, (25, 17837): 219.2016305205295, (25, 17838): 219.4485802114282, (25, 17862): 218.29741496323228, (25, 17866): 221.66440153730002, (25, 17872): 217.09970927862142, (25, 17873): 214.54502918650624, (25, 17881): 218.4773336029718, (25, 17947): 414.97475238868395, (25, 17951): 411.54257227513267, (25, 17953): 410.8851720275566, (25, 17954): 411.12468784839126, (25, 17959): 414.2725889425891, (25, 17963): 413.0704687410744, (25, 18000): 395.6300797306564, (25, 18001): 396.3053610162431, (25, 18111): 446.3075182779495, (25, 18148): 358.27302492345973, (25, 18166): 392.64934351729363, (25, 18189): 424.0720326154081, (25, 18239): 227.1162136483001, (25, 18240): 227.10965371759852, (25, 18245): 227.27251827764698, (25, 18247): 226.93528466159898, (25, 18251): 227.2820756455251, (25, 18256): 227.6736328358798, (25, 18258): 227.27920339116912, (25, 18259): 227.35924614732278, (25, 18260): 227.52627445547037, (25, 18262): 227.83353459969246, (25, 18263): 227.78704620149003, (25, 18264): 227.95207810321025, (25, 18266): 227.9661834122061, (25, 18267): 228.12639615064538, (25, 18268): 228.21105114156202, (25, 18269): 228.5327900422762, (25, 18275): 228.38098919348337, (25, 18285): 227.8904002692511, (25, 18308): 224.5679858983076, (25, 18313): 223.4776818257542, (25, 18314): 224.00204441519517, (25, 18315): 228.47327295078105, (25, 18316): 228.46754220507827, (25, 18317): 228.61918579087492, (25, 18320): 228.73189076379617, (25, 18321): 228.8244527399425, (25, 18322): 229.05924716859235, (25, 18324): 229.22068037108147, (25, 18325): 229.9215316299781, (25, 18326): 229.65945912678114, (25, 18327): 228.77642028905524, (25, 18329): 230.21352974643145, (25, 18330): 229.92887458204856, (25, 18331): 229.44866945137198, (25, 18332): 228.96551490743238, (25, 18333): 229.8362221348695, (25, 18336): 229.41151487087456, (25, 18337): 229.63673656224216, (25, 18403): 229.40533249340942, (25, 18432): 220.78040489162947, (25, 18451): 226.5793798191191, (25, 18466): 232.37734693112284, (25, 18481): 228.60428984156778, (25, 18483): 228.6175944977833, (25, 18484): 228.22190559848184, (25, 18485): 227.0203339187331, (25, 18486): 228.00965521309777, (25, 18487): 227.10184668795222, (25, 18489): 227.94306544062763, (25, 18490): 228.80298493917851, (25, 18491): 229.22414138006135, (25, 18492): 226.21170782033568, (25, 18493): 227.84643520841988, (25, 18494): 227.782163748764, (25, 18495): 228.48738255249845, (25, 18496): 228.0557908489886, (25, 18497): 226.88306102474414, (25, 18498): 227.13443554418615, (25, 18499): 227.79509832961824, (25, 18501): 227.2959102075316, (25, 18502): 226.8723202460234, (25, 18503): 226.56131587888336, (25, 18504): 228.24545768390433, (25, 18506): 227.3269570995603, (25, 18507): 226.91777916434629, (25, 18508): 227.6911847563328, (25, 18509): 227.68830632006174, (25, 18510): 226.55610205198596, (25, 18511): 227.95115252860356, (25, 18512): 227.47386196366529, (25, 18515): 228.26768804145976, (25, 18516): 228.26217825397606, (25, 18517): 227.7123646970153, (25, 18518): 228.620578310793, (25, 18519): 228.34431167518974, (25, 18520): 227.5810310913642, (25, 18522): 230.1678365303153, (25, 18523): 230.24341547892902, (25, 18532): 230.80701668082904, (25, 18535): 229.61995847924075, (25, 18537): 228.95916060448323, (25, 18539): 229.0888917926652, (25, 18540): 229.15703401009037, (25, 18541): 229.47530906975882, (25, 18542): 229.67895793105458, (25, 18543): 228.66124540386545, (25, 18546): 229.11845394983686, (25, 18555): 230.154142255547, (25, 18556): 230.33270758103765, (25, 18565): 230.70898738512437, (25, 18567): 230.9820134329039, (25, 18568): 230.42966854096997, (25, 18577): 234.4890061994205, (25, 18583): 233.8485709773857, (25, 18605): 234.75448643473035, (25, 18608): 231.27602759585506, (25, 18616): 238.53689638984085, (25, 18618): 241.73306133789856, (25, 18625): 240.74747707593343, (25, 18645): 237.96157155503627, (25, 18646): 238.65632789288733, (25, 18653): 235.84647202240947, (25, 18654): 238.4358635905423, (25, 18655): 236.71005412152653, (25, 18666): 247.38223632140233, (25, 18837): 240.67404239995204, (25, 18974): 227.2818251113672, (25, 18999): 230.452803595724, (25, 19000): 231.4216158829897, (25, 19174): 191.2071980474856, (25, 19342): 212.1225315391906, (25, 19455): 193.89899297046085, (25, 19555): 151.91223876989616, (25, 19564): 158.873544164258, (25, 19573): 156.02537220240123, (25, 19586): 154.46668238583632, (25, 19605): 154.4766780486118, (25, 19611): 156.22541194972038, (25, 19614): 154.26098001449535, (25, 19641): 178.3237229569438, (25, 19702): 179.15973009093662, (25, 19713): 177.1364212697957, (25, 19731): 138.69764484199212, (25, 19819): 188.55254839100152, (25, 19893): 143.68363849996075, (25, 19899): 157.69332356594452, (25, 19929): 146.38142375316636, (25, 19951): 170.72890188517866, (25, 19962): 150.24042121060359, (25, 19970): 151.88338079194514, (25, 19971): 152.81516176920275, (25, 19972): 151.38200349182912, (25, 19975): 149.83206144093575, (25, 19978): 172.27208756049384, (25, 19987): 172.19031920830506, (25, 19989): 165.5395989996558, (25, 20039): 173.17496694173994, (25, 20043): 175.28631206125308, (25, 20047): 172.5875283755067, (25, 20052): 165.76436326937008, (25, 20054): 166.6547969218444, (25, 20085): 195.809941392006, (25, 20104): 197.75451937960847, (25, 20132): 186.43733079489766, (25, 20203): 151.19626563172963, (25, 20280): 151.69632885214287, (25, 20285): 152.3991868497834, (25, 20290): 152.19323436283244, (25, 20297): 149.77130363731214, (25, 20309): 179.66581975127627, (25, 20453): 208.3237240762301, (25, 20485): 134.87817881713676, (25, 20520): 128.61207136377053, (25, 20526): 130.03906913176064, (25, 20698): 256.8211383039574, (25, 20868): 311.8954485950441, (25, 21042): 56.107072378934554, (25, 21057): 69.3842261475815, (25, 21066): 62.550563978202334, (25, 21075): 60.557303399781816, (25, 21093): 56.713306572928396, (25, 21098): 65.82396596081006, (25, 21127): 56.960531801154076, (25, 21130): 59.28990751542247, (25, 21144): 59.28573960252433, (25, 21146): 56.097771055561374, (25, 21147): 59.21422943992488, (25, 21148): 61.33997907120845, (25, 21153): 59.16579651558877, (25, 21293): 77.49431433659285, (25, 21426): 83.80085457628209, (25, 21442): 100.04402537576343, (25, 21451): 101.53723733273853, (25, 21466): 91.06706531455633, (25, 21469): 92.73947197002371, (25, 21471): 90.2585286090163, (25, 21473): 91.45080931585443, (25, 21475): 90.17911399557404, (25, 21482): 94.39499298859126, (25, 21484): 93.73165501312668, (25, 21488): 92.91400495118232, (25, 21494): 89.3335306438258, (25, 21498): 90.79942097794027, (25, 21500): 87.83803475843948, (25, 21514): 88.98196125589509, (25, 21537): 85.72213615546464, (25, 21662): 89.15380845195452, (25, 21691): 81.41945399501013, (25, 21757): 74.28544385654406, (25, 21777): 31.43413774118961, (25, 21778): 29.486135644142728, (25, 21779): 31.072510824023276, (25, 21790): 33.24998347388737, (25, 21802): 33.92616831068569, (25, 21824): 36.43485177177752, (25, 21874): 32.29252453507562, (25, 21879): 32.55106690208003, (25, 21983): 37.54591145343684, (25, 22002): 59.92355838049496, (25, 22132): 55.39181389425785, (25, 22261): 247.82462211683224, (25, 22298): 244.71215539173903, (25, 22339): 271.11089175201556, (25, 22508): 207.90507269904617, (25, 22841): 669.2967412268129, (25, 22842): 669.2859424228819, (25, 22874): 664.2760077968306, (25, 22941): 664.8520929683781, (25, 22956): 667.8512219782268, (25, 22960): 668.7908918917735, (25, 22968): 671.4784988818184, (25, 22970): 672.3482073453189, (25, 22974): 673.6514813878337, (25, 22980): 677.27375690705, (25, 23025): 676.6379254434662, (25, 23028): 675.77258562649, (25, 23081): 681.5349719524454, (25, 23104): 674.5582605027245, (25, 23147): 643.2839123660129, (25, 23298): 120.82216177480348, (25, 23376): 114.9197401798309, (25, 23381): 110.1366071512737, (25, 23529): 123.52448805699323, (25, 23556): 120.2553598911864, (25, 23718): 118.64258042863759, (25, 24001): 156.04455116235684, (25, 24094): 164.98033145220646, (25, 24129): 170.81925770742845, (25, 24174): 158.255899437365, (25, 24235): 170.9947957708599, (25, 24259): 176.76007148294067, (25, 24260): 176.3064794727498, (25, 24261): 175.09150435391362, (25, 24305): 183.5156390587715, (25, 24306): 184.58591944505085, (25, 24307): 182.92113293894008, (25, 24308): 172.41714939512983, (25, 24498): 199.35638568358183, (25, 24499): 199.4502785546749, (25, 24500): 198.40939860877134, (25, 24668): 193.35863266846061, (25, 24711): 205.9789557256289, (25, 24756): 209.53412803100022, (25, 24788): 211.32447372335392, (25, 24809): 204.6121524801638, (25, 24813): 206.70988984935596, (25, 24821): 206.0249554235193, (25, 24825): 206.5050307648271, (25, 24832): 204.17895863178686, (25, 24833): 205.18187997173217, (25, 24835): 206.17407051582964, (25, 24837): 207.78940670751402, (25, 24840): 204.01626835296955, (25, 24841): 205.58260988715432, (25, 24844): 204.05256429372398, (25, 24845): 205.00814443703754, (25, 24846): 204.86439170847058, (25, 24849): 205.40601663645572, (25, 24850): 207.00057567062296, (25, 24863): 193.12376224651007, (25, 24866): 194.92086067052423, (25, 24885): 197.01147830481682, (25, 24886): 197.14736542955086, (25, 24889): 201.17712182997383, (25, 24903): 202.76730362201948, (25, 24909): 196.28166179023287, (25, 24999): 276.62397518028956, (25, 25019): 274.98266972138094, (25, 25028): 275.4245971223988, (25, 25137): 170.42956846719548, (25, 25145): 171.91847521964186, (25, 25208): 203.3783887218587, (25, 25233): 201.71933947566416, (25, 25371): 161.48043652119222, (25, 25377): 154.18319670177334, (25, 25828): 91.90122279161534, (25, 25851): 82.36453844507358, (25, 25874): 85.06234456560817, (25, 25898): 95.51924959475055, (25, 25946): 91.17477673621248, (25, 26047): 117.57237370297669, (25, 26066): 104.39704479832618, (25, 26197): 103.10776458109589, (25, 26212): 133.58008944385617, (25, 26253): 138.73775194187377, (25, 26254): 136.08329770224748, (25, 26257): 136.45881525051288, (25, 26258): 138.31911122666827, (25, 26260): 137.1941185594313, (25, 26266): 134.25427612732548, (25, 26267): 133.6535835649208, (25, 26271): 134.2154142182603, (25, 26304): 114.4661580334497, (25, 26305): 112.9372211054651, (25, 26363): 103.39134260115418, (25, 26441): 269.39451761301143, (25, 26442): 268.5996759339134, (25, 26450): 265.4715087895804, (25, 26459): 265.85902020597223, (25, 26462): 266.5827497865121, (25, 26467): 275.8485279705316, (25, 26471): 272.92911191543067, (25, 26472): 272.560984903486, (25, 26473): 272.3651273668368, (25, 26476): 269.9872171855816, (25, 26485): 267.114991161998, (25, 26493): 266.8909603280782, (25, 26524): 268.2644028471846, (25, 26525): 267.72121845827417, (25, 26556): 271.7049497199018, (25, 26560): 271.933616675085, (25, 26561): 270.06033920254924, (25, 26564): 270.70574304375015, (25, 26569): 269.392642982401, (25, 26570): 268.38929081458724, (25, 26573): 268.6158121467708, (25, 26581): 268.29864042302626, (25, 26583): 267.75736958931276, (25, 26593): 268.01771674777206, (25, 26837): 276.23136877709106, (25, 26844): 278.4641638766254, (25, 26863): 273.0292803392581, (25, 26893): 279.2253419049344, (25, 26902): 282.2369185594906, (25, 26905): 279.6914079085856, (25, 26912): 281.8804219457688, (25, 26921): 276.03130529838717, (25, 26922): 269.2229061136194, (25, 27212): 306.2337562355379, (25, 27218): 304.42979579956835, (25, 27239): 310.1969410925235, (25, 27257): 307.77698405492157, (25, 27274): 310.8819599744939, (25, 27279): 310.12230026615657, (25, 27282): 307.7074174606847, (25, 27283): 309.2435205332521, (25, 27285): 311.79696876469836, (25, 27286): 309.0649232468848, (25, 27290): 305.5945307789862, (25, 27295): 304.55846359579226, (25, 27300): 311.41637793381625, (25, 27344): 303.60500506516996, (25, 27366): 306.055431649982, (25, 27383): 311.3881229514124, (25, 27398): 315.05654326329676, (25, 27406): 312.8710470980241, (25, 27407): 313.8233686774739, (25, 27426): 312.73211557951305, (25, 27432): 301.683094623074, (25, 27460): 308.89253036221277, (25, 27523): 302.51111169561455, (25, 27545): 350.43567325641567, (25, 27602): 403.9363944420802, (25, 27606): 405.2226167457499, (25, 27646): 343.1757864089163, (25, 27667): 354.107549731469, (25, 27672): 354.84952953169096, (25, 27674): 352.88069669235347, (25, 27688): 355.1126614626349, (25, 27692): 356.5490340281539, (25, 27693): 354.87642044764556, (25, 27705): 354.6003844781973, (25, 27712): 355.26364018259176, (25, 27786): 413.4385596785843, (25, 27790): 409.88172732868674, (25, 27791): 409.749387698121, (25, 27795): 410.1585541139394, (25, 27801): 407.25947281442785, (25, 27813): 414.8337993712297, (25, 27816): 413.3439534317758, (25, 27823): 407.17452036820026, (25, 27830): 411.51974443068247, (25, 27884): 322.9370406341705, (25, 27885): 338.28130627672857, (25, 27896): 329.11030641521126, (25, 27919): 328.666403664737, (25, 27922): 330.2966070027957, (25, 27930): 325.5115391097026, (25, 27934): 325.9314033646594, (25, 27935): 326.17418322797516, (25, 27948): 390.45649829584534, (25, 27951): 395.9103054099548, (25, 28061): 325.6344496010399, (25, 28290): 445.5610487983487, (25, 28292): 447.5737919542236, (25, 28293): 445.9175144679658, (25, 28295): 444.6193456338208, (25, 28296): 445.2899623316942, (25, 28297): 444.46603149097825, (25, 28302): 443.35018704551356, (25, 28310): 479.4397008844518, (25, 28313): 481.45462260404224, (25, 28372): 481.4688481011966, (25, 28398): 481.6815258705605, (25, 28399): 480.92027660922884, (25, 28400): 482.1932358356397, (25, 28401): 478.81587015934934, (25, 28445): 480.4025751693448, (25, 28475): 476.07364309342466, (25, 28885): 169.7841896973157, (25, 28886): 168.68071924669258, (25, 28915): 169.60711726891003, (25, 28916): 168.68412758906754, (25, 28917): 168.09753995434158, (25, 28921): 171.8296908289604, (25, 28931): 171.51355145703448, (25, 28945): 166.3544246358982, (25, 28982): 167.49093766252432, (25, 29219): 175.19235065836153, (25, 29228): 170.29911590357696, (25, 29246): 203.49814878117715, (25, 29248): 203.72991418845044, (25, 29282): 196.92211095994733, (25, 29290): 206.13136972352757, (25, 29291): 204.96001247022502, (25, 29292): 206.13978744543368, (25, 29293): 203.51828274880927, (25, 29294): 205.8564837835468, (25, 29298): 203.87222630828936, (25, 29299): 203.81036027177655, (25, 29304): 201.00895083846765, (25, 29317): 194.52509933480326, (25, 29323): 194.00587479146023, (25, 29330): 197.1527203941866, (25, 29331): 198.59230706070554, (25, 29344): 176.88400577250107, (25, 29445): 125.39890546184319, (25, 29724): 660.7481435550997, (25, 29738): 661.7131314640757, (25, 29745): 658.8904490826518, (25, 29748): 659.4152766497873, (25, 29750): 660.9822250206125, (25, 29759): 658.0955990495567, (25, 29772): 661.6613690866492, (25, 29781): 660.8821086443609, (25, 29784): 660.2840043647658, (25, 29790): 661.6538836972124, (25, 29811): 659.6143957535597, (25, 29817): 666.1883972750493, (25, 29818): 665.4313567616489, (25, 29929): 658.5777420142289, (25, 30039): 671.3114149367467, (25, 30066): 663.2962326369822, (25, 30116): 630.2922699554352, (25, 30238): 581.5293322783464, (25, 30248): 605.6022134242811, (25, 30260): 606.1613728463694, (25, 30545): 153.47727634491386, (25, 30733): 101.8665854654914, (25, 30756): 87.11786594729517, (25, 30921): 112.36679399757995, (25, 31079): 101.36365774161132, (25, 31149): 85.96733000997308, (25, 31154): 88.56236053924273, (25, 31160): 85.6553835550546, (25, 31163): 88.59815791865515, (25, 31189): 87.36651631639877, (25, 31215): 89.4385184068938, (25, 31259): 100.82459130679611, (25, 31262): 100.34394422876517, (25, 31430): 109.56114244973207, (25, 31568): 135.37684335236474, (25, 31751): 106.54926465363955, (27, 109): 204.95275806069614, (27, 872): 368.6346211067077, (27, 873): 371.04322336296923, (27, 877): 370.07878316615626, (27, 879): 370.4305477491733, (27, 884): 367.8780655020719, (27, 889): 369.416993300682, (27, 891): 367.09512083475335, (27, 892): 372.3115695474689, (27, 894): 372.0314473802908, (27, 896): 369.81362504446696, (27, 903): 370.10235205533826, (27, 909): 366.2044164928496, (27, 910): 367.22979987223044, (27, 912): 365.62455902940474, (27, 913): 363.8325779361042, (27, 916): 363.16848738112327, (27, 926): 368.10221836997977, (27, 927): 367.30983895477743, (27, 948): 366.23026634842824, (27, 961): 367.86929384025416, (27, 962): 368.1851666441772, (27, 963): 368.5268178552253, (27, 967): 371.14546535143256, (27, 974): 369.7203692245463, (27, 998): 372.0535460135814, (27, 1014): 425.4759864504432, (27, 1086): 365.1684983046272, (27, 1087): 365.2587650936914, (27, 1089): 362.86463100243384, (27, 1090): 363.83208749970396, (27, 1092): 367.25101460579555, (27, 1097): 364.56691581310565, (27, 1107): 369.197337232148, (27, 1387): 107.72843266263277, (27, 1554): 110.24154617912099, (27, 1827): 479.4025359184486, (27, 1828): 479.660540583297, (27, 1829): 480.0403083604533, (27, 1830): 479.66960530952656, (27, 1831): 479.8865777009347, (27, 1832): 479.61948485120763, (27, 1833): 479.64578811788766, (27, 1836): 479.3583555165017, (27, 1841): 480.9408969749106, (27, 1843): 480.27982470616394, (27, 1844): 480.5777198396944, (27, 1845): 479.79378651655963, (27, 1847): 477.2362984068875, (27, 1848): 478.1144727632152, (27, 1849): 482.236096504389, (27, 1850): 482.66383641064783, (27, 1851): 478.79596281601783, (27, 1852): 478.86960600398953, (27, 1854): 479.2830998968611, (27, 1856): 477.1213561075571, (27, 1857): 478.0585889197645, (27, 1858): 481.82936947572693, (27, 1861): 479.99077345763016, (27, 1866): 477.0727604910164, (27, 1867): 480.97986879785026, (27, 1868): 480.4436565103605, (27, 1870): 480.5168698087503, (27, 1871): 480.8541361993046, (27, 1875): 479.232538502886, (27, 1880): 477.6644573637543, (27, 1882): 477.93600086832856, (27, 1883): 482.6879955141886, (27, 1889): 478.1119792374797, (27, 1893): 480.0788608627573, (27, 1894): 479.4572890311071, (27, 1899): 477.56105015016544, (27, 1900): 478.01641749532354, (27, 1902): 481.1550902433412, (27, 1905): 481.959029324466, (27, 1907): 478.7044139388877, (27, 1910): 478.9921662640041, (27, 1917): 483.62714205384736, (27, 1920): 478.75902757306477, (27, 1935): 482.05828537115116, (27, 1937): 482.74140202221406, (27, 1946): 476.17409032911405, (27, 1949): 476.9347162451279, (27, 1950): 474.26721393748096, (27, 1951): 475.55624239576997, (27, 1952): 476.5394026243714, (27, 1953): 476.944455865543, (27, 1954): 476.3461500880295, (27, 1958): 476.7218563866778, (27, 1960): 478.0200140552522, (27, 1968): 478.53253692284005, (27, 1969): 482.20709714394127, (27, 1974): 481.2464347631636, (27, 1975): 481.2395332494007, (27, 1979): 479.3945670839808, (27, 1980): 479.2604541747945, (27, 1981): 479.79086672692085, (27, 1985): 480.23083751208065, (27, 1994): 473.26420244683686, (27, 2011): 477.91127293070144, (27, 2019): 484.38531766265476, (27, 2020): 483.5284554151074, (27, 2029): 480.3066705410434, (27, 2030): 482.9342179682746, (27, 2032): 479.79645861248343, (27, 2033): 481.4916855910353, (27, 2034): 481.47817306923764, (27, 2036): 478.3270484080218, (27, 2037): 479.1291671080047, (27, 2038): 479.3276266774959, (27, 2042): 489.15582176253935, (27, 2050): 481.02747679365325, (27, 2051): 480.9015776592625, (27, 2053): 481.15525237017283, (27, 2054): 482.02507773256906, (27, 2066): 480.25784045294245, (27, 2067): 480.255511402779, (27, 2071): 471.62143829938395, (27, 2072): 473.23880857361735, (27, 2073): 468.7554554196985, (27, 2074): 468.5403143240169, (27, 2080): 465.8102255664853, (27, 2082): 474.11357442517794, (27, 2083): 474.9492596672022, (27, 2089): 473.1577936163924, (27, 2090): 473.93590416390725, (27, 2092): 472.86098530791895, (27, 2098): 466.84805233588065, (27, 2099): 467.7998782333765, (27, 2101): 466.68604712577735, (27, 2102): 471.1061639801633, (27, 2103): 469.7202829877551, (27, 2104): 468.9672879160326, (27, 2106): 475.52195592119926, (27, 2112): 467.2831132574851, (27, 2113): 471.7413683120733, (27, 2114): 472.8255272881615, (27, 2117): 476.19654643157287, (27, 2123): 469.8551348440887, (27, 2124): 470.7672509462968, (27, 2134): 468.1241096672139, (27, 2138): 470.8247600660905, (27, 2141): 468.4531116752564, (27, 2148): 469.6666029568152, (27, 2150): 466.22537809436596, (27, 2151): 467.1737468804627, (27, 2152): 465.7103060874549, (27, 2153): 469.98208562514753, (27, 2154): 466.2090418442668, (27, 2155): 465.7602682626741, (27, 2156): 465.06682737453673, (27, 2157): 465.99051427936223, (27, 2160): 472.0296629625382, (27, 2161): 465.53807952619985, (27, 2162): 470.1156122572621, (27, 2163): 468.8363253093978, (27, 2164): 468.7475420683869, (27, 2168): 466.5237771959857, (27, 2172): 467.3330247682385, (27, 2174): 467.0447997849453, (27, 2178): 468.072471471511, (27, 2179): 467.48045280482586, (27, 2183): 470.7437352303008, (27, 2185): 470.7917437262799, (27, 2186): 470.0686686595129, (27, 2190): 472.22236486686495, (27, 2192): 470.9165181881424, (27, 2193): 471.00486604755514, (27, 2194): 469.67192161283026, (27, 2195): 469.45845337766195, (27, 2197): 471.1939911122454, (27, 2205): 469.30411792344495, (27, 2207): 466.8515268992249, (27, 2208): 468.2202218327872, (27, 2212): 471.443755325584, (27, 2214): 444.24075300659416, (27, 2225): 447.4424770153925, (27, 2231): 441.51166812794435, (27, 2278): 460.8106974732797, (27, 2284): 463.5909434258164, (27, 2285): 463.2152529670256, (27, 2291): 457.8155045645201, (27, 2292): 458.321716900144, (27, 2307): 461.79925621666774, (27, 2313): 457.2041203728176, (27, 2317): 456.26048160204874, (27, 2319): 459.27804781188826, (27, 2321): 460.5579935292806, (27, 2323): 460.36996509214464, (27, 2326): 465.16358483208285, (27, 2327): 463.9694533108211, (27, 2329): 463.15577254971276, (27, 2330): 462.23210090977426, (27, 2332): 464.20693105896794, (27, 2344): 461.1423569392115, (27, 2346): 461.0947359354662, (27, 2361): 460.6180751886187, (27, 2368): 474.530662747047, (27, 2374): 475.8496037203383, (27, 2375): 476.2857580434773, (27, 2377): 471.694997226658, (27, 2378): 477.1164624365283, (27, 2379): 477.24023513053146, (27, 2380): 477.6874871833967, (27, 2383): 472.9162207938277, (27, 2385): 473.6232009885249, (27, 2395): 473.7001503334458, (27, 2397): 476.6986757276921, (27, 2398): 470.2335036903745, (27, 2399): 471.88205200445145, (27, 2400): 471.511994658626, (27, 2402): 474.14765102806626, (27, 2403): 475.1741355973676, (27, 2404): 475.4353498905302, (27, 2405): 472.9646073360852, (27, 2407): 474.9732318387881, (27, 2408): 476.18060100719816, (27, 2409): 473.71294540837465, (27, 2411): 475.18214192226554, (27, 2412): 474.90633486557215, (27, 2413): 475.75114514906477, (27, 2414): 474.3835174930618, (27, 2422): 474.8757130594717, (27, 2424): 475.1928468589051, (27, 2426): 475.412372316477, (27, 2433): 473.5041842011972, (27, 2436): 473.0053320485553, (27, 2437): 467.00716983117707, (27, 2440): 468.32638153692824, (27, 2445): 495.06964474152386, (27, 2447): 491.76928394933833, (27, 2454): 494.84987040429814, (27, 2455): 495.00028903921833, (27, 2460): 485.46304504523584, (27, 2461): 486.64446515200274, (27, 2471): 505.87943404238706, (27, 2492): 487.3070118985263, (27, 2511): 477.29335990834727, (27, 2523): 482.4150521492637, (27, 2525): 481.0868506549377, (27, 2535): 482.57730939339115, (27, 2537): 480.4803183096065, (27, 2538): 481.891280190145, (27, 2539): 481.4585583457753, (27, 2540): 483.5332273629352, (27, 2542): 485.115322605169, (27, 2559): 514.8533551867433, (27, 2575): 512.3256540370879, (27, 2599): 466.45565882173446, (27, 2600): 476.69780832128333, (27, 2607): 470.7170887993981, (27, 2627): 484.2701400593686, (27, 2647): 490.14269060971293, (27, 2674): 486.87575724482565, (27, 2681): 486.2683240286267, (27, 2683): 488.93829083248704, (27, 2686): 485.6960530203122, (27, 2689): 522.552724554835, (27, 2690): 522.7769562151744, (27, 2713): 531.4495143779722, (27, 2714): 532.3105311862566, (27, 2715): 533.2030809526216, (27, 2739): 532.3392419880399, (27, 2740): 526.0491489827637, (27, 2741): 526.4487289919368, (27, 2749): 531.3667158811958, (27, 2750): 531.557387012821, (27, 2752): 532.1541878599802, (27, 2755): 532.9161706401242, (27, 2758): 532.7845581339199, (27, 2759): 532.7477083366406, (27, 2769): 531.6092612052645, (27, 2771): 527.6589331117511, (27, 2779): 528.559820631206, (27, 2784): 518.7650085424679, (27, 2800): 521.2432399207123, (27, 2802): 524.6377697361792, (27, 2803): 524.2203290076748, (27, 2804): 523.5915123132969, (27, 2805): 525.6280230356961, (27, 2807): 525.4923560545551, (27, 2809): 525.337779162497, (27, 2812): 519.3837765953732, (27, 2814): 525.5850992717391, (27, 2817): 526.5711977839978, (27, 2819): 525.4168877685189, (27, 2823): 520.6532368011888, (27, 2832): 526.8555287479165, (27, 2836): 522.8071803657188, (27, 2839): 525.3992462148748, (27, 2841): 526.3645078022207, (27, 2843): 525.9238922548386, (27, 2846): 523.937950003919, (27, 2849): 527.6245110555769, (27, 2852): 526.6528939208517, (27, 2853): 528.0768797467567, (27, 2876): 528.876055540044, (27, 2877): 532.1819153863403, (27, 2885): 534.0041483958424, (27, 2918): 525.3907248575396, (27, 2921): 526.8776743718611, (27, 2925): 519.6787365077854, (27, 2926): 517.1617177148019, (27, 2930): 523.2477240625988, (27, 2931): 520.4770593338709, (27, 2938): 525.538415626969, (27, 2940): 529.0059641884969, (27, 2947): 524.0753409637465, (27, 2949): 522.9100639811892, (27, 2950): 523.6668776162338, (27, 2952): 522.9796628160435, (27, 2958): 522.7920922995938, (27, 2959): 523.3112686511454, (27, 2960): 524.8993643590793, (27, 2961): 524.2185398595103, (27, 2963): 522.2811932150919, (27, 2968): 522.7980913644064, (27, 2976): 522.0192905215359, (27, 2981): 509.86557658152435, (27, 2982): 509.6598121700377, (27, 2984): 509.0185660657072, (27, 3003): 508.0163940890012, (27, 3046): 497.2491281859327, (27, 3050): 505.0906027468934, (27, 3051): 505.56842808925626, (27, 3053): 504.1323725168676, (27, 3069): 512.8054879473999, (27, 3071): 503.4082815436618, (27, 3080): 534.3429871861739, (27, 3199): 506.9346779100982, (27, 3200): 505.48780240723215, (27, 3205): 515.1129676952047, (27, 3209): 506.33565979927425, (27, 3215): 505.4759120122218, (27, 3217): 503.56126579208114, (27, 3249): 505.53571588146224, (27, 3263): 519.9541245954148, (27, 3289): 509.80297113058714, (27, 3301): 510.5398740807845, (27, 3302): 509.7469184279753, (27, 3307): 508.8572163013939, (27, 3310): 511.3648203457558, (27, 3391): 519.4557714506848, (27, 3509): 194.3206468886294, (27, 3510): 192.9378884927419, (27, 3511): 193.68631373431708, (27, 3512): 192.68197857574242, (27, 3514): 192.84080989878478, (27, 3519): 198.44803733914685, (27, 3536): 196.46153059069192, (27, 3545): 198.46790757653648, (27, 3548): 196.13399086163685, (27, 3572): 197.45206323380046, (27, 3581): 196.36633645712627, (27, 3583): 194.70123370515367, (27, 3601): 201.33407044095185, (27, 3656): 199.8633550462771, (27, 3669): 199.0113684152535, (27, 3670): 200.32115640948012, (27, 3695): 192.50062653199572, (27, 3696): 193.4380896786088, (27, 3782): 194.4181776074762, (27, 3792): 193.15719113029118, (27, 3989): 407.16161173019884, (27, 4008): 414.64250532280016, (27, 4031): 414.0954890953633, (27, 4045): 411.4981180840421, (27, 4144): 411.9780884122472, (27, 4145): 404.58112832070935, (27, 4164): 409.11335254972704, (27, 4168): 406.8303199761066, (27, 4173): 406.37975281694577, (27, 4181): 401.8303902887444, (27, 4228): 397.4123104044674, (27, 4248): 395.71214319041, (27, 4254): 355.89522004853364, (27, 4260): 355.93738669816236, (27, 4262): 358.61177482013596, (27, 4273): 357.9778050447577, (27, 4319): 333.9508515076681, (27, 4326): 333.1114203485849, (27, 4328): 333.3988263832598, (27, 4334): 335.02298191560885, (27, 4335): 334.45641749932116, (27, 4372): 337.5011432712829, (27, 4413): 362.25060538494284, (27, 4434): 336.22987966681274, (27, 4447): 338.5430420656555, (27, 4452): 336.69383700417075, (27, 4463): 294.4667146462402, (27, 4465): 295.65880427558966, (27, 4619): 367.73211713016866, (27, 4645): 372.238782658664, (27, 4657): 371.80073236643375, (27, 4666): 370.19224332577613, (27, 4676): 373.62926168108595, (27, 4678): 374.23490199245106, (27, 4689): 372.3000587873614, (27, 4704): 389.443753333313, (27, 4726): 437.5204005297988, (27, 4727): 436.66103615843286, (27, 4730): 434.9751808624064, (27, 4731): 435.58610665162877, (27, 4734): 435.80677302654817, (27, 4735): 435.1003845561613, (27, 4736): 435.6035906858257, (27, 4737): 434.28711578273084, (27, 4738): 434.55552132715127, (27, 4756): 435.47207335801556, (27, 4760): 430.6457944270156, (27, 4761): 430.92784165768785, (27, 4762): 429.59709585471205, (27, 4765): 431.1292679387356, (27, 4773): 439.1064350957427, (27, 4774): 438.49637797559404, (27, 4790): 438.512291557336, (27, 4795): 437.72318441805083, (27, 4799): 438.95132920018426, (27, 4801): 440.9695686283918, (27, 4804): 437.8222551750649, (27, 4805): 437.17697920128995, (27, 4806): 438.40292010116406, (27, 4815): 437.71904773401985, (27, 4816): 439.80069749070566, (27, 4817): 440.4117497825183, (27, 4826): 439.0714230610657, (27, 4830): 437.92830965355915, (27, 4839): 433.1520048778286, (27, 4840): 433.9924856374858, (27, 4841): 432.24689401666853, (27, 4846): 431.622798529511, (27, 4848): 431.5802892557926, (27, 4850): 432.38588526537023, (27, 4871): 421.76826209868386, (27, 4883): 429.46349988712024, (27, 4900): 425.30073826438354, (27, 4901): 424.35175743224875, (27, 4917): 370.36154350368224, (27, 4931): 364.27401209047474, (27, 4944): 370.93261732007636, (27, 4956): 365.5098483866974, (27, 4958): 365.57307412619804, (27, 4959): 364.5836953290696, (27, 4961): 366.6458539099496, (27, 4966): 364.1603688073487, (27, 5207): 357.4408183561604, (27, 5272): 235.7555884154906, (27, 5283): 237.9757327179334, (27, 5287): 241.6742598391246, (27, 5289): 242.66206508225548, (27, 5293): 236.08307211424378, (27, 5295): 242.25975004870068, (27, 5296): 242.274733087681, (27, 5298): 242.2411427436747, (27, 5303): 244.14929852354095, (27, 5305): 234.62145703188298, (27, 5306): 233.03565376275924, (27, 5307): 233.47633898496863, (27, 5308): 235.67524628398564, (27, 5313): 235.4683808003843, (27, 5314): 236.83775188501156, (27, 5317): 235.75824803661828, (27, 5319): 242.0296245172638, (27, 5324): 240.7099570807021, (27, 5326): 239.8647842902076, (27, 5348): 232.62066996257659, (27, 5351): 234.47203731896616, (27, 5399): 244.1030962499913, (27, 5413): 237.72439686042577, (27, 5422): 245.1818282822353, (27, 5445): 240.13911807989845, (27, 5448): 238.01893074349618, (27, 5456): 237.65118245545992, (27, 5467): 239.66456306964716, (27, 5624): 216.1826596603902, (27, 5671): 283.8899124772673, (27, 5672): 281.0397030937569, (27, 5797): 318.13634387259305, (27, 5871): 276.47267952278435, (27, 5976): 251.1175986195206, (27, 6118): 377.0246616000769, (27, 6248): 413.4375235139928, (27, 6345): 143.1524250314836, (27, 6352): 139.11497504919657, (27, 6354): 143.76986290545824, (27, 6359): 145.31614260774845, (27, 6376): 141.64138611167044, (27, 6378): 143.35337931257814, (27, 6381): 145.47330836757487, (27, 6383): 141.98299456055005, (27, 6396): 147.9580006976221, (27, 6399): 144.09086072671283, (27, 6408): 138.48748817188684, (27, 6409): 138.45482635838007, (27, 6419): 128.73379409356664, (27, 6422): 137.45402110619386, (27, 6423): 137.01357221969346, (27, 6424): 141.26592176030863, (27, 6439): 139.84540150308337, (27, 6464): 138.07351887980752, (27, 6465): 138.2799899240712, (27, 6469): 140.17739337053777, (27, 6470): 140.24127652449081, (27, 6472): 147.03101949808402, (27, 6480): 143.11732644487213, (27, 6486): 142.91819731780876, (27, 6497): 142.78715528430408, (27, 6503): 134.85825036133335, (27, 6508): 137.0289592409873, (27, 6509): 137.06127765126845, (27, 6521): 142.39020806698082, (27, 6544): 140.35143280401277, (27, 6552): 134.85189421448737, (27, 6553): 133.97360905763153, (27, 6554): 133.107092166225, (27, 6578): 136.59340131894677, (27, 6582): 134.07642216540407, (27, 6601): 136.58480535683282, (27, 6609): 145.25948686270283, (27, 6610): 145.1004523143893, (27, 6611): 146.28980732912007, (27, 6614): 146.48868041254076, (27, 6615): 146.27330683283242, (27, 6616): 145.7979829043039, (27, 6617): 145.88415069022892, (27, 6618): 145.79102835716486, (27, 6619): 145.6862556243951, (27, 6620): 145.1944242494973, (27, 6621): 144.3611964416327, (27, 6622): 144.95687816765076, (27, 6623): 145.7050785135994, (27, 6624): 144.4122181351714, (27, 6625): 144.62820523533836, (27, 6626): 145.93479587454945, (27, 6627): 146.89503483583619, (27, 6628): 144.42318438058408, (27, 6629): 143.82785355792623, (27, 6630): 145.08283244815044, (27, 6632): 144.10633409358002, (27, 6634): 143.91660626387025, (27, 6635): 144.44398451273938, (27, 6636): 145.62133777123216, (27, 6637): 142.79442826787528, (27, 6638): 144.5403199242316, (27, 6639): 146.58085911107997, (27, 6640): 144.98808905501195, (27, 6641): 143.86100714471596, (27, 6642): 144.12277200953596, (27, 6643): 146.32871764261347, (27, 6645): 145.48614694726328, (27, 6646): 146.01890613974697, (27, 6647): 144.57172156396854, (27, 6653): 146.44229228004903, (27, 6655): 146.80277301285815, (27, 6658): 143.60755977750435, (27, 6662): 143.62123609065222, (27, 6819): 96.2144967459697, (27, 6996): 100.20605968254345, (27, 7059): 110.83132395132778, (27, 7187): 86.03942162294554, (27, 7304): 64.00477320520783, (27, 7528): 94.23088179259003, (27, 7720): 163.47097445217815, (27, 7793): 161.116381940409, (27, 7807): 162.32235071193088, (27, 7808): 160.60025335878098, (27, 7831): 146.46875500928428, (27, 7850): 158.76818771795854, (27, 7852): 157.354750450088, (27, 8012): 162.2545905603327, (27, 8125): 168.40819060339692, (27, 8208): 183.97671126171718, (27, 8392): 147.27330938611433, (27, 8651): 64.1716085521181, (27, 9088): 111.1222907155273, (27, 9443): 24.0, (27, 9444): 24.0, (27, 9828): 64.26232863834271, (27, 9868): 57.69513234744444, (27, 10180): 169.80113100675968, (27, 10256): 199.80449812457746, (27, 10276): 185.4899620485451, (27, 10378): 188.85176667775582, (27, 10676): 164.70015094916175, (27, 10714): 147.61169476217793, (27, 10730): 145.8813265566176, (27, 10862): 239.41178427061163, (27, 10881): 243.18787970829462, (27, 10883): 243.17826406110476, (27, 10885): 238.49838219156808, (27, 10891): 243.18565820208002, (27, 10909): 241.87298101661804, (27, 10911): 241.4011410813265, (27, 10913): 240.84993405464516, (27, 10915): 240.2934023149673, (27, 10919): 240.38882907903934, (27, 11037): 229.3324693372624, (27, 11039): 215.47056594776893, (27, 11516): 487.28602780514404, (27, 11856): 335.73809696312145, (27, 11857): 334.59797147217677, (27, 11861): 335.20534924964636, (27, 11881): 334.037222192362, (27, 11902): 328.93991561632276, (27, 11911): 328.0987010021502, (27, 11914): 328.7691977119467, (27, 11922): 332.52905947109497, (27, 11924): 333.7503963513218, (27, 11926): 332.2870696028373, (27, 11950): 335.27957737855223, (27, 11963): 340.0594408912163, (27, 11983): 336.96322933193426, (27, 11985): 342.45068710016136, (27, 12009): 341.632145070499, (27, 12010): 338.21158774372105, (27, 12018): 338.78756756925475, (27, 12020): 339.68932530727915, (27, 12021): 340.2647892364438, (27, 12024): 343.50537628534084, (27, 12025): 342.3849322764036, (27, 12027): 341.6235462141098, (27, 12031): 337.6436991858657, (27, 12032): 338.75162973833653, (27, 12035): 341.4470120569986, (27, 12041): 342.80567357693013, (27, 12045): 297.8500615638113, (27, 12145): 318.78041615351987, (27, 12275): 410.4291750057445, (27, 12294): 402.4215031353515, (27, 12358): 429.4466318675845, (27, 12463): 440.3150877808068, (27, 12465): 440.04702750032476, (27, 12482): 443.99015680354853, (27, 12503): 443.499804834868, (27, 12506): 444.70774326202985, (27, 12549): 441.46305663683285, (27, 12559): 440.66366333865665, (27, 12569): 441.8769859080351, (27, 12572): 442.7729062885118, (27, 12574): 440.83092020588896, (27, 12576): 442.4409520780807, (27, 12591): 441.87936811966364, (27, 12608): 448.9900672794582, (27, 12696): 436.9892939343736, (27, 12710): 443.4676561826166, (27, 12728): 440.5508599769935, (27, 12766): 242.66313799846776, (27, 12771): 230.99508850953828, (27, 12790): 229.87344232254623, (27, 12795): 227.63413753059734, (27, 12797): 214.2779433835489, (27, 12798): 215.7979741452807, (27, 12811): 225.36906574464987, (27, 12830): 222.6386689503399, (27, 12848): 223.3548323321679, (27, 12850): 223.61667800373883, (27, 12852): 221.89400933996959, (27, 12854): 220.4356368504422, (27, 12859): 224.56875590657495, (27, 12861): 217.1992731434652, (27, 12865): 227.58062537212282, (27, 12866): 226.54775124019122, (27, 12867): 229.72239065555425, (27, 12874): 228.22178519311916, (27, 12875): 229.20493620087163, (27, 12881): 225.00768622926248, (27, 12883): 226.77611407527607, (27, 12885): 230.2263996261294, (27, 12888): 225.7527660391858, (27, 12889): 225.16108790924793, (27, 12892): 228.64342869556944, (27, 12893): 226.0152253280771, (27, 12896): 226.684241783992, (27, 12906): 229.20586295303067, (27, 13018): 222.71379425913116, (27, 13071): 224.52195493494423, (27, 13131): 206.98431902630077, (27, 13146): 215.14484526590275, (27, 13159): 210.745632166601, (27, 13193): 204.74654599368827, (27, 13198): 185.99494864522137, (27, 13292): 204.20129287521453, (27, 13296): 207.5015402246316, (27, 13406): 180.5403587399842, (27, 13407): 180.4332139480256, (27, 13417): 182.68285073277266, (27, 13418): 184.93064770461092, (27, 13438): 189.05541220207024, (27, 13442): 189.3545451444389, (27, 13443): 188.16370509027053, (27, 13764): 145.38786969942285, (27, 13766): 145.7920882639133, (27, 13771): 148.27901735650738, (27, 13783): 140.23951307996336, (27, 13784): 145.02505320348342, (27, 13792): 151.952487782746, (27, 13824): 140.55219033348436, (27, 14017): 126.90688805585268, (27, 14870): 219.34349135499215, (27, 14997): 77.95012086491006, (27, 15000): 78.57340391049111, (27, 15003): 80.28344437901454, (27, 15006): 81.23563002824585, (27, 15007): 82.52432229460963, (27, 15056): 83.5246998565239, (27, 15063): 82.67488952498377, (27, 15069): 82.80841943446154, (27, 15076): 82.9685376292464, (27, 15086): 78.5984918059584, (27, 15087): 77.72315950559992, (27, 15111): 73.608087619148, (27, 15116): 76.00306634646392, (27, 15722): 42.516425311244234, (27, 15998): 53.42941644233101, (27, 16073): 299.69231528919875, (27, 16939): 402.1902185842508, (27, 16940): 400.3618644493731, (27, 16951): 402.56777741808764, (27, 16963): 402.711571398482, (27, 16965): 404.8832498892006, (27, 16969): 404.4237722310787, (27, 16970): 403.47318766001774, (27, 16971): 401.51160539580457, (27, 16973): 401.42712126510133, (27, 16974): 405.8002064287884, (27, 16976): 403.59719459154456, (27, 16978): 402.14807047450114, (27, 16980): 404.2863245880562, (27, 16982): 405.8346518140335, (27, 17045): 474.4964517924289, (27, 17048): 477.0439726731346, (27, 17304): 385.0897826362715, (27, 17305): 383.8397629676093, (27, 17330): 385.03784300012387, (27, 17334): 382.6195030459788, (27, 17343): 386.89278353475066, (27, 17345): 382.5443004277102, (27, 17347): 384.8820907506494, (27, 17351): 379.26719145927535, (27, 17372): 382.3486390479232, (27, 17373): 386.74443211403184, (27, 17377): 387.0549781004699, (27, 17382): 384.19555252553585, (27, 17383): 384.7208959302105, (27, 17389): 383.03482675612423, (27, 17400): 385.9424769912398, (27, 17401): 385.88305934486715, (27, 17402): 386.1132025425348, (27, 17403): 386.3997319048955, (27, 17440): 382.7487884743128, (27, 17455): 386.4092585598097, (27, 17491): 386.7073898894822, (27, 17507): 380.91680160018956, (27, 17509): 382.511113840786, (27, 17590): 378.21825635282363, (27, 17615): 369.53987356818647, (27, 17642): 371.09874864789475, (27, 17643): 370.9371945348195, (27, 17668): 369.49321199059057, (27, 17721): 365.950120493464, (27, 17754): 380.98487384209164, (27, 17769): 381.47752844460615, (27, 17776): 375.09708872325007, (27, 17804): 384.0672803554304, (27, 17809): 385.6635910176631, (27, 17824): 384.65077844959137, (27, 17837): 379.9308087247204, (27, 17838): 380.0987210621511, (27, 17862): 378.90947568888026, (27, 17866): 382.30991063931646, (27, 17872): 377.7651352502872, (27, 17873): 375.1661706607423, (27, 17881): 379.1534002487958, (27, 17947): 255.60319740373131, (27, 17951): 252.0660511626769, (27, 17953): 251.47010586693375, (27, 17954): 251.77139846471556, (27, 17959): 254.74088867987126, (27, 17963): 253.3703844601395, (27, 18000): 235.65521170680557, (27, 18001): 236.4424956848332, (27, 18111): 293.0534628544285, (27, 18148): 204.4640449752002, (27, 18166): 240.04180942081416, (27, 18189): 270.5294692601077, (27, 18239): 387.5502409297856, (27, 18240): 387.52366920553834, (27, 18245): 387.69586624017035, (27, 18247): 387.33788776460864, (27, 18251): 387.6807964089854, (27, 18256): 388.04407313300015, (27, 18258): 387.63847227868297, (27, 18259): 387.70698751646125, (27, 18260): 387.85762364465205, (27, 18262): 388.149254965213, (27, 18263): 388.14533238990106, (27, 18264): 388.2955466238266, (27, 18266): 388.2622739288238, (27, 18267): 388.4105206227277, (27, 18268): 388.480980486412, (27, 18269): 388.7760291539839, (27, 18275): 388.6367681449205, (27, 18285): 388.2472400478045, (27, 18308): 385.16519376819343, (27, 18313): 384.09959919250895, (27, 18314): 384.55799765550574, (27, 18315): 388.7791017307767, (27, 18316): 388.745455712475, (27, 18317): 388.8828494158237, (27, 18320): 389.0250509476157, (27, 18321): 389.096522112705, (27, 18322): 389.3148587630695, (27, 18324): 389.50530948280027, (27, 18325): 390.19650038484406, (27, 18326): 389.93938778816135, (27, 18327): 389.00159324003846, (27, 18329): 390.5168974114129, (27, 18330): 390.1443461722018, (27, 18331): 389.68573067009885, (27, 18332): 389.20906503296436, (27, 18333): 390.0797319193108, (27, 18336): 389.70487813812883, (27, 18337): 389.9454304881821, (27, 18403): 389.5480717863625, (27, 18432): 379.95740875489616, (27, 18451): 386.4438290305938, (27, 18466): 392.8318787611641, (27, 18481): 388.98290443987173, (27, 18483): 388.9765043842814, (27, 18484): 388.60102590794406, (27, 18485): 387.4777291167657, (27, 18486): 388.51895605287945, (27, 18487): 387.64313980299625, (27, 18489): 388.392028886534, (27, 18490): 389.29057685297806, (27, 18491): 389.70658179812875, (27, 18492): 386.7491501452102, (27, 18493): 388.3785072912243, (27, 18494): 388.21811136500065, (27, 18495): 388.98150253319585, (27, 18496): 388.54049545937113, (27, 18497): 387.4473844253344, (27, 18498): 387.6250381539732, (27, 18499): 388.2707850723561, (27, 18501): 387.81402914830346, (27, 18502): 387.4017149411496, (27, 18503): 387.07793683570503, (27, 18504): 388.7054204771319, (27, 18506): 387.8933665583774, (27, 18507): 387.50397772140644, (27, 18508): 388.186541849818, (27, 18509): 388.2004247515213, (27, 18510): 387.09697549561866, (27, 18511): 388.51553050304415, (27, 18512): 388.01626839815685, (27, 18515): 388.7527639851588, (27, 18516): 388.8046765370248, (27, 18517): 388.29287031802875, (27, 18518): 389.14039950872706, (27, 18519): 388.7915064018147, (27, 18520): 388.0574697647948, (27, 18522): 390.5376770357546, (27, 18523): 390.63293588654403, (27, 18532): 391.21527378868063, (27, 18535): 390.01090888786763, (27, 18537): 389.34035200275457, (27, 18539): 389.48323940137965, (27, 18540): 389.56414735153413, (27, 18541): 389.8966352191212, (27, 18542): 390.10725704493194, (27, 18543): 389.0631341485372, (27, 18546): 389.56794724226967, (27, 18555): 390.6198533166712, (27, 18556): 390.8148661173017, (27, 18565): 391.1440042347404, (27, 18567): 391.4612473189936, (27, 18568): 390.88339294702223, (27, 18577): 394.9958413691733, (27, 18583): 394.29231313529914, (27, 18605): 395.14186291724144, (27, 18608): 391.8360419099667, (27, 18616): 398.98060338496583, (27, 18618): 402.2553404110714, (27, 18625): 401.1084754773785, (27, 18645): 398.2119061413952, (27, 18646): 398.9723837237166, (27, 18653): 396.2704278020343, (27, 18654): 398.9021297715415, (27, 18655): 397.17865644736963, (27, 18666): 407.7509175909108, (27, 18837): 396.6982412599352, (27, 18974): 386.4121702099796, (27, 18999): 389.2077238312597, (27, 19000): 390.1947680520228, (27, 19174): 344.7909329526752, (27, 19342): 365.3545922112219, (27, 19455): 350.8557655283019, (27, 19555): 303.8740375278912, (27, 19564): 308.4646833345275, (27, 19573): 306.00106126715735, (27, 19586): 304.78943506140655, (27, 19605): 305.29420934697185, (27, 19611): 306.8860572315063, (27, 19614): 305.7016108123817, (27, 19641): 330.2004310151702, (27, 19702): 330.2973330269567, (27, 19713): 328.39556200848915, (27, 19731): 293.6382707564586, (27, 19819): 344.18024259351637, (27, 19893): 286.9722024507951, (27, 19899): 298.6174520653178, (27, 19929): 289.8989363603065, (27, 19951): 312.6055359266114, (27, 19962): 291.9869377442799, (27, 19970): 296.5136296128396, (27, 19971): 296.7110224763568, (27, 19972): 294.8759198973895, (27, 19975): 293.90975117872034, (27, 19978): 316.94336077117464, (27, 19987): 317.27949097488096, (27, 19989): 311.0542625478687, (27, 20039): 318.4009109214771, (27, 20043): 320.93751134178837, (27, 20047): 318.8962204177986, (27, 20052): 312.0659677345061, (27, 20054): 312.63283316168673, (27, 20085): 343.47225877990263, (27, 20104): 345.4092251972181, (27, 20132): 333.59109410396246, (27, 20203): 286.9669337246927, (27, 20280): 284.9092588338727, (27, 20285): 284.4946884900767, (27, 20290): 285.90683913584775, (27, 20297): 283.72247081458113, (27, 20309): 319.3216754272997, (27, 20453): 351.1156096165176, (27, 20485): 270.0755526229804, (27, 20520): 264.56227165317677, (27, 20526): 263.01176352220983, (27, 20698): 193.45186705729606, (27, 20868): 218.423615699121, (27, 21042): 217.05079124709204, (27, 21057): 230.2610275473886, (27, 21066): 223.57881922005285, (27, 21075): 221.40021927425474, (27, 21093): 217.77203187181615, (27, 21098): 226.80040427949865, (27, 21127): 217.98649338158353, (27, 21130): 220.34685857473016, (27, 21144): 220.23092534644493, (27, 21146): 217.12577985773586, (27, 21147): 220.0956871648782, (27, 21148): 222.28631978963597, (27, 21153): 218.21154082008098, (27, 21293): 238.5378451553047, (27, 21426): 239.24263541615252, (27, 21442): 254.35647888481225, (27, 21451): 255.78883801962652, (27, 21466): 246.44412119145898, (27, 21469): 248.40128707724188, (27, 21471): 245.46466435339198, (27, 21473): 247.01294411701087, (27, 21475): 245.55126672247408, (27, 21482): 249.86495236720737, (27, 21484): 249.33741753430024, (27, 21488): 248.25255834611372, (27, 21494): 245.22568476225834, (27, 21498): 246.76575370851265, (27, 21500): 244.0873429473188, (27, 21514): 247.13846146811866, (27, 21537): 243.00562567305127, (27, 21662): 248.3171554564113, (27, 21691): 240.29978227056824, (27, 21757): 228.2305629031516, (27, 21777): 191.02368413122022, (27, 21778): 188.98925556652736, (27, 21779): 190.07239751399777, (27, 21790): 193.38545726881688, (27, 21802): 193.15927257336696, (27, 21824): 195.2307901257114, (27, 21874): 190.5513825690113, (27, 21879): 189.31425450816428, (27, 21983): 198.60607634322128, (27, 22002): 219.92592016306756, (27, 22132): 210.19863539032823, (27, 22261): 107.14148351373997, (27, 22298): 106.79926243434045, (27, 22339): 133.0700115234926, (27, 22508): 78.33671487749841, (27, 22841): 531.1179365849592, (27, 22842): 530.9543358866323, (27, 22874): 525.5197579458945, (27, 22941): 526.6047326956648, (27, 22956): 529.4124539878469, (27, 22960): 530.7008741916856, (27, 22968): 531.2805006658471, (27, 22970): 532.4250161858522, (27, 22974): 532.44764746, (27, 22980): 535.9927238077553, (27, 23025): 533.6241513945813, (27, 23028): 532.4232903090317, (27, 23081): 536.0340279120855, (27, 23104): 526.529182073505, (27, 23147): 500.41979925892633, (27, 23298): 281.1624811645156, (27, 23376): 275.2718156828886, (27, 23381): 271.0482267789777, (27, 23529): 284.3267905053881, (27, 23556): 281.0093329023937, (27, 23718): 278.2566888633346, (27, 24001): 316.1784679578195, (27, 24094): 325.90174229567265, (27, 24129): 331.7288905593612, (27, 24174): 319.30433711440577, (27, 24235): 332.0551003200645, (27, 24259): 337.79135165767485, (27, 24260): 337.34552402832537, (27, 24261): 336.1249366071583, (27, 24305): 344.51213711564077, (27, 24306): 345.59536354078335, (27, 24307): 343.9246053706972, (27, 24308): 331.6395800255257, (27, 24498): 359.90423676774043, (27, 24499): 360.01228877619457, (27, 24500): 358.95763016195, (27, 24668): 352.8486334481535, (27, 24711): 366.7949978146163, (27, 24756): 370.4959100136895, (27, 24788): 372.2292816915614, (27, 24809): 365.633950681063, (27, 24813): 367.6946687550435, (27, 24821): 367.0195194909034, (27, 24825): 367.50838862153785, (27, 24832): 365.19607778071435, (27, 24833): 366.19360896439747, (27, 24835): 367.1845003334446, (27, 24837): 368.77928180300927, (27, 24840): 365.0388292808914, (27, 24841): 366.58644815503163, (27, 24844): 365.0807683359658, (27, 24845): 366.00505663705434, (27, 24846): 365.89757011723424, (27, 24849): 366.4393846103814, (27, 24850): 367.99346716482574, (27, 24863): 354.14517280219934, (27, 24866): 355.9298957087892, (27, 24885): 358.031618444564, (27, 24886): 358.1795349379091, (27, 24889): 362.12069351739814, (27, 24903): 363.65610649391476, (27, 24909): 357.1686586563673, (27, 24999): 435.3177910402004, (27, 25019): 433.40199038364005, (27, 25028): 434.21573547931365, (27, 25137): 292.5321062772612, (27, 25145): 294.659737955361, (27, 25208): 323.07113898186134, (27, 25233): 320.33975862243466, (27, 25371): 290.3871925812492, (27, 25377): 283.59109800424466, (27, 25828): 171.40377797909483, (27, 25851): 152.09304630038068, (27, 25874): 168.8239214348957, (27, 25898): 178.5161125700458, (27, 25946): 169.5378270694094, (27, 26047): 209.48309373502178, (27, 26066): 240.74325069833765, (27, 26197): 217.91347802716686, (27, 26212): 135.23819241756743, (27, 26253): 132.79603154242238, (27, 26254): 133.17322207316846, (27, 26257): 135.69842142287422, (27, 26258): 133.75698049361176, (27, 26260): 134.623750802822, (27, 26266): 129.86406319618595, (27, 26267): 131.51330783839464, (27, 26271): 132.0176090638522, (27, 26304): 141.03138379079508, (27, 26305): 139.91562267824446, (27, 26363): 169.6723936853351, (27, 26441): 156.79807131703168, (27, 26442): 155.7170932281283, (27, 26450): 153.67789708116877, (27, 26459): 156.2079447062139, (27, 26462): 157.6842819576265, (27, 26467): 164.11248155798992, (27, 26471): 160.94784084191173, (27, 26472): 160.364965305049, (27, 26473): 159.91422870538221, (27, 26476): 155.0140717150749, (27, 26485): 155.94486049395263, (27, 26493): 154.63844227939808, (27, 26524): 159.83422254834235, (27, 26525): 158.84759407472208, (27, 26556): 160.1941922887249, (27, 26560): 162.19684343437564, (27, 26561): 161.34010858039554, (27, 26564): 158.99329991625913, (27, 26569): 160.26622967496138, (27, 26570): 158.8656328740053, (27, 26573): 158.02325190600683, (27, 26581): 156.92117601812288, (27, 26583): 157.09612200739386, (27, 26593): 155.6118486527453, (27, 26837): 163.51488542907492, (27, 26844): 165.5125168951355, (27, 26863): 158.66676947034216, (27, 26893): 163.44889382738688, (27, 26902): 166.11948449597165, (27, 26905): 165.60423825234324, (27, 26912): 166.9807414240037, (27, 26921): 161.0970857341167, (27, 26922): 152.2826530087968, (27, 27212): 228.0039339339511, (27, 27218): 228.4260176113283, (27, 27239): 230.59492516729756, (27, 27257): 228.17053849186127, (27, 27274): 230.76675943774467, (27, 27279): 229.52386750094416, (27, 27282): 227.74898252366575, (27, 27283): 230.18888246304962, (27, 27285): 231.04079397393514, (27, 27286): 227.84863529640003, (27, 27290): 226.09377944730707, (27, 27295): 226.36210079007017, (27, 27300): 231.4259869669259, (27, 27344): 222.6337731854853, (27, 27366): 223.7654500181832, (27, 27383): 229.33409658662538, (27, 27398): 233.69107985831232, (27, 27406): 232.55252952217126, (27, 27407): 233.79256015916388, (27, 27426): 237.5312809182063, (27, 27432): 228.18174487832428, (27, 27460): 234.8524854187404, (27, 27523): 210.56526294121295, (27, 27545): 259.4292099950437, (27, 27602): 300.25532848558066, (27, 27606): 301.96781416298916, (27, 27646): 239.8091543806392, (27, 27667): 248.47407787839992, (27, 27672): 249.4945222833711, (27, 27674): 247.6556705848741, (27, 27688): 251.12562558683078, (27, 27692): 250.3707955357147, (27, 27693): 248.9395691709389, (27, 27705): 248.23457305871165, (27, 27712): 248.4041113610695, (27, 27786): 323.7394044115154, (27, 27790): 326.3269643827915, (27, 27791): 327.0242510615678, (27, 27795): 320.5758196839022, (27, 27801): 321.80627106705236, (27, 27813): 324.26878626929084, (27, 27816): 324.12255491154866, (27, 27823): 321.92493095537424, (27, 27830): 323.88360388768587, (27, 27884): 218.8033230955009, (27, 27885): 235.18890995980996, (27, 27896): 225.642079548836, (27, 27919): 225.62892439116976, (27, 27922): 226.70403383664788, (27, 27930): 222.13388356405707, (27, 27934): 222.17765000354785, (27, 27935): 221.97559993973567, (27, 27948): 269.6169483038008, (27, 27951): 280.4602569551633, (27, 28061): 171.48975252510562, (27, 28290): 294.9712148218341, (27, 28292): 296.1799686273501, (27, 28293): 295.10296197496086, (27, 28295): 293.2874142531343, (27, 28296): 294.4208483255535, (27, 28297): 294.25866070065376, (27, 28302): 292.66367167735945, (27, 28310): 326.1130033042636, (27, 28313): 328.9159284359904, (27, 28372): 327.38795544355986, (27, 28398): 327.70803415336314, (27, 28399): 327.05419852261184, (27, 28400): 328.3468452853362, (27, 28401): 324.7312458777746, (27, 28445): 328.3761447115182, (27, 28475): 320.948440929695, (27, 28885): 330.01250829245816, (27, 28886): 328.8292535187427, (27, 28915): 329.4467081222964, (27, 28916): 328.6214635807783, (27, 28917): 327.9568200534256, (27, 28921): 332.13160498217786, (27, 28931): 331.7412043129816, (27, 28945): 325.28034976874164, (27, 28982): 326.9153173208327, (27, 29219): 331.93329714403643, (27, 29228): 327.07552668661697, (27, 29246): 358.3064460834111, (27, 29248): 357.8048779146955, (27, 29282): 351.2590298919261, (27, 29290): 361.6049517235128, (27, 29291): 360.2666514665889, (27, 29292): 361.50636388582217, (27, 29293): 358.9504262158627, (27, 29294): 360.9463912327063, (27, 29298): 359.11940953989154, (27, 29299): 358.87744558605795, (27, 29304): 356.5435735085752, (27, 29317): 350.4532267992783, (27, 29323): 349.98445192052293, (27, 29330): 352.91125002193394, (27, 29331): 354.3906553130103, (27, 29344): 332.21761386849244, (27, 29445): 276.13123059664264, (27, 29724): 529.3639515225296, (27, 29738): 530.2871756935331, (27, 29745): 527.8497902979279, (27, 29748): 529.6977670216029, (27, 29750): 531.767306859407, (27, 29759): 528.2706480821794, (27, 29772): 531.699419291694, (27, 29781): 530.9888720338029, (27, 29784): 529.834878679027, (27, 29790): 531.9695073496589, (27, 29811): 530.613583369398, (27, 29817): 540.5491137780367, (27, 29818): 539.8874083217207, (27, 29929): 526.722242944841, (27, 30039): 535.3933026387014, (27, 30066): 525.7145605964463, (27, 30116): 496.7038448683794, (27, 30238): 454.3968191838133, (27, 30248): 471.31754332470825, (27, 30260): 471.48133966081645, (27, 30545): 314.40047905960915, (27, 30733): 262.85882616852797, (27, 30756): 247.33110541267396, (27, 30921): 273.1805928261668, (27, 31079): 169.34457359715694, (27, 31149): 155.7560043661621, (27, 31154): 157.00145492272867, (27, 31160): 155.21653386554604, (27, 31163): 156.1885038192518, (27, 31189): 132.3396731710666, (27, 31215): 134.83883630029015, (27, 31259): 137.87585212956486, (27, 31262): 135.00628396386998, (27, 31430): 175.21862071057055, (27, 31568): 130.29696564841683, (27, 31751): 160.57566812468448, (28, 109): 571.1642213261615, (28, 872): 91.04170331445673, (28, 873): 89.58038268401496, (28, 877): 88.94012064547891, (28, 879): 88.60781967706723, (28, 884): 87.48484600853907, (28, 889): 87.09007182315014, (28, 891): 88.30642534263245, (28, 892): 87.73629732645229, (28, 894): 88.40409621637163, (28, 896): 91.76254900717721, (28, 903): 87.53655344867384, (28, 909): 93.93686531545481, (28, 910): 94.42359445231295, (28, 912): 95.16049614099344, (28, 913): 95.60218570645641, (28, 916): 97.36555647175494, (28, 926): 95.37876649079395, (28, 927): 96.11460581615542, (28, 948): 89.05593988489436, (28, 961): 92.87155773075925, (28, 962): 93.4664418084261, (28, 963): 93.89216047790558, (28, 967): 87.39699203813203, (28, 974): 85.43870523841954, (28, 998): 85.84797305379499, (28, 1014): 85.38970754631053, (28, 1086): 126.6924307168344, (28, 1087): 130.86754791820655, (28, 1089): 129.93113992560023, (28, 1090): 129.0657165140363, (28, 1092): 127.2625293289271, (28, 1097): 127.8404665615227, (28, 1107): 128.96085522620572, (28, 1387): 451.5992343111703, (28, 1554): 481.76239378943205, (28, 1827): 82.4004037198951, (28, 1828): 82.82930532435516, (28, 1829): 83.00624321528491, (28, 1830): 81.74454004196954, (28, 1831): 82.09410599515262, (28, 1832): 81.9543724196897, (28, 1833): 82.13787939911798, (28, 1836): 82.07764431937618, (28, 1841): 83.19234820265099, (28, 1843): 82.6248991789224, (28, 1844): 82.7243343614988, (28, 1845): 81.91304459321621, (28, 1847): 80.21696745243987, (28, 1848): 80.89664345818777, (28, 1849): 84.01101915568195, (28, 1850): 84.4944938241027, (28, 1851): 80.99852034683876, (28, 1852): 80.70004317048574, (28, 1854): 81.31169975083704, (28, 1856): 79.61547038724957, (28, 1857): 80.64384183783464, (28, 1858): 83.92549332041922, (28, 1861): 82.6373853264163, (28, 1866): 79.25387919661449, (28, 1867): 83.53632695825169, (28, 1868): 83.39130540718268, (28, 1870): 82.2177695426527, (28, 1871): 83.74821084406108, (28, 1875): 81.5159052141707, (28, 1880): 80.38757651370715, (28, 1882): 80.06920844088769, (28, 1883): 84.91402039115324, (28, 1889): 81.40220447244651, (28, 1893): 83.68800349768462, (28, 1894): 83.30013154941507, (28, 1899): 81.23378135818334, (28, 1900): 81.74468683512336, (28, 1902): 84.56872826042193, (28, 1905): 84.97541986632503, (28, 1907): 81.77605162580801, (28, 1910): 82.50749516656042, (28, 1917): 87.64819326396923, (28, 1920): 82.17323026001903, (28, 1935): 85.82004998820037, (28, 1937): 86.24736828510005, (28, 1946): 81.10938756158536, (28, 1949): 81.9535900601652, (28, 1950): 78.66124657659951, (28, 1951): 80.0046083145487, (28, 1952): 79.72506050451794, (28, 1953): 81.05744122743322, (28, 1954): 79.82418691048495, (28, 1958): 81.296412673178, (28, 1960): 82.08431647635318, (28, 1968): 82.40483434617428, (28, 1969): 86.75369184908224, (28, 1974): 85.5414191360881, (28, 1975): 85.26177640309724, (28, 1979): 84.25249725440024, (28, 1980): 83.29702510510381, (28, 1981): 84.27016441123816, (28, 1985): 84.87694814882248, (28, 1994): 75.93742531975865, (28, 2011): 79.80792449184679, (28, 2019): 84.73762985296783, (28, 2020): 84.05657836523864, (28, 2029): 80.96411288464122, (28, 2030): 83.5972961713794, (28, 2032): 80.18195438173582, (28, 2033): 82.09383845871274, (28, 2034): 81.80049216514945, (28, 2036): 77.77410541164821, (28, 2037): 78.82936726002794, (28, 2038): 80.31699276627887, (28, 2042): 89.01549452178752, (28, 2050): 82.11945570974878, (28, 2051): 81.68629399854005, (28, 2053): 82.04770243573738, (28, 2054): 82.79583860461965, (28, 2066): 81.22192198388463, (28, 2067): 81.38873293679224, (28, 2071): 74.80154519900773, (28, 2072): 76.45088300860552, (28, 2073): 74.02914864580866, (28, 2074): 73.54636287217502, (28, 2080): 70.6117137816879, (28, 2082): 77.24840003183891, (28, 2083): 78.12694498726954, (28, 2089): 76.93647288188207, (28, 2090): 77.8285183371128, (28, 2092): 77.19222786261017, (28, 2098): 72.06707214698885, (28, 2099): 72.53477931035266, (28, 2101): 71.5040844056906, (28, 2102): 75.6292655120349, (28, 2103): 74.16275497697175, (28, 2104): 73.17047415807582, (28, 2106): 78.45243908898996, (28, 2112): 71.66377402018875, (28, 2113): 75.97424111865124, (28, 2114): 76.31815003206796, (28, 2117): 78.78337970802086, (28, 2123): 94.73421442028634, (28, 2124): 95.43757009556808, (28, 2134): 91.58551920650886, (28, 2138): 94.40292833757037, (28, 2141): 92.39635301043329, (28, 2148): 86.66638278369327, (28, 2150): 90.34892928247741, (28, 2151): 90.55771444487095, (28, 2152): 89.4715171598502, (28, 2153): 87.53325976878605, (28, 2154): 84.87835986646927, (28, 2155): 83.40324754459492, (28, 2156): 83.64401942013052, (28, 2157): 80.44076664586555, (28, 2160): 92.10418671032158, (28, 2161): 88.6371465577553, (28, 2162): 85.27066929548529, (28, 2163): 84.40763678649732, (28, 2164): 83.95733481390846, (28, 2168): 87.01085493157616, (28, 2172): 84.62146436709013, (28, 2174): 89.57816691495525, (28, 2178): 84.36919557485248, (28, 2179): 83.64119791148408, (28, 2183): 93.54157430280527, (28, 2185): 93.1561357294621, (28, 2186): 92.81264350119928, (28, 2190): 92.98227611701947, (28, 2192): 92.18987465708278, (28, 2193): 93.9839190200911, (28, 2194): 93.2064545531975, (28, 2195): 92.15972176254034, (28, 2197): 91.92194721242033, (28, 2205): 89.51463315297711, (28, 2207): 86.66790381114967, (28, 2208): 88.08051864632856, (28, 2212): 96.26543179251895, (28, 2214): 64.22414535599582, (28, 2225): 63.41240887542651, (28, 2231): 83.30717378935974, (28, 2278): 67.85008718392405, (28, 2284): 69.05147570524768, (28, 2285): 68.33268199857162, (28, 2291): 61.18905219626536, (28, 2292): 64.92700888432948, (28, 2307): 67.49442358970425, (28, 2313): 59.747561389035795, (28, 2317): 64.84961377901372, (28, 2319): 65.34294856789263, (28, 2321): 65.82053958451009, (28, 2323): 66.62829843634205, (28, 2326): 72.31163258302264, (28, 2327): 71.36330983593172, (28, 2329): 70.6164624020083, (28, 2330): 69.52933934885651, (28, 2332): 70.6381664213628, (28, 2344): 69.69448598464695, (28, 2346): 68.91837559601495, (28, 2361): 75.3287626216692, (28, 2368): 82.07305160346691, (28, 2374): 82.64526922390507, (28, 2375): 83.3234078052256, (28, 2377): 80.1361294202731, (28, 2378): 83.73077180884317, (28, 2379): 83.20904166931197, (28, 2380): 84.01706811490524, (28, 2383): 81.52167624162799, (28, 2385): 82.32095106701684, (28, 2395): 83.01033463290256, (28, 2397): 82.48466032877758, (28, 2398): 79.07852590693918, (28, 2399): 80.6776538655724, (28, 2400): 80.4074434659828, (28, 2402): 80.59406179816916, (28, 2403): 81.38086514861048, (28, 2404): 81.83959964877172, (28, 2405): 79.72202721219504, (28, 2407): 81.82337885693762, (28, 2408): 82.4760979530809, (28, 2409): 80.4625011941305, (28, 2411): 80.3703310795702, (28, 2412): 80.53020186152487, (28, 2413): 81.05377609542153, (28, 2414): 79.84559957837772, (28, 2422): 79.78525503445856, (28, 2424): 80.97665373334647, (28, 2426): 81.35577257231519, (28, 2433): 79.46705569755265, (28, 2436): 78.40413489843714, (28, 2437): 74.00538233158069, (28, 2440): 75.14808297625684, (28, 2445): 94.06428906128109, (28, 2447): 91.25459627532975, (28, 2454): 94.12035151356514, (28, 2455): 94.48786123876098, (28, 2460): 85.36297957474194, (28, 2461): 86.43083477143087, (28, 2471): 103.701869736963, (28, 2492): 89.16898368482406, (28, 2511): 77.04327520194418, (28, 2523): 83.24155129659665, (28, 2525): 82.58864128361564, (28, 2535): 79.98582719770657, (28, 2537): 77.90795538784393, (28, 2538): 79.2586003875164, (28, 2539): 79.19482739020437, (28, 2540): 80.9402256811553, (28, 2542): 82.61396866763374, (28, 2559): 112.19459158956009, (28, 2575): 109.70640683929604, (28, 2599): 65.84465992141212, (28, 2600): 74.9245413417166, (28, 2607): 70.52033170319544, (28, 2627): 90.51361976651665, (28, 2647): 97.78317627865422, (28, 2674): 92.15868684382176, (28, 2681): 92.73427603680994, (28, 2683): 94.80181530472335, (28, 2686): 91.07834928808893, (28, 2689): 128.353527797332, (28, 2690): 128.81682134596343, (28, 2713): 145.57123554278832, (28, 2714): 147.6665711091211, (28, 2715): 148.45402022641588, (28, 2739): 147.30882688272126, (28, 2740): 138.18612125553722, (28, 2741): 138.30343491924856, (28, 2749): 147.83837666593018, (28, 2750): 147.53368349794425, (28, 2752): 147.84669050726976, (28, 2755): 148.8142330316381, (28, 2758): 149.09284090730958, (28, 2759): 148.84891829523016, (28, 2769): 147.30988633957253, (28, 2771): 140.53164760231385, (28, 2779): 144.67941615158975, (28, 2784): 137.6704963789884, (28, 2800): 143.58526729195174, (28, 2802): 138.6568570827334, (28, 2803): 137.8653018602445, (28, 2804): 137.13531581595868, (28, 2805): 140.82087222347178, (28, 2807): 140.26800092450665, (28, 2809): 141.09982609604612, (28, 2812): 134.69144832879843, (28, 2814): 144.30607811360204, (28, 2817): 149.43577936622972, (28, 2819): 139.1607486114877, (28, 2823): 139.7740080180375, (28, 2832): 142.53204294909673, (28, 2836): 138.8666580275542, (28, 2839): 139.75073915245312, (28, 2841): 147.060597898311, (28, 2843): 145.9148000929272, (28, 2846): 141.70002126336604, (28, 2849): 143.96607792438664, (28, 2852): 142.8057430078158, (28, 2853): 144.53188753934884, (28, 2876): 147.3353541420211, (28, 2877): 150.61069410547915, (28, 2885): 156.6360188315587, (28, 2918): 136.54971795651826, (28, 2921): 138.40467235279883, (28, 2925): 128.29686931350625, (28, 2926): 124.20077531242929, (28, 2930): 135.97394002994628, (28, 2931): 130.0735392666945, (28, 2938): 137.37171581973604, (28, 2940): 137.57111615818226, (28, 2947): 132.09990622443158, (28, 2949): 134.079723813309, (28, 2950): 135.46447734021672, (28, 2952): 134.84242001042213, (28, 2958): 134.38589918215382, (28, 2959): 134.0949312558176, (28, 2960): 135.84506061174002, (28, 2961): 135.51107067250456, (28, 2963): 134.30569385644446, (28, 2968): 135.19935864870808, (28, 2976): 133.64437015106927, (28, 2981): 128.07927322941418, (28, 2982): 128.89710701128922, (28, 2984): 128.5780946937172, (28, 3003): 128.8568027160846, (28, 3046): 108.40655906098807, (28, 3050): 120.35813248497686, (28, 3051): 120.41961571825138, (28, 3053): 119.55409432458646, (28, 3069): 128.754002660114, (28, 3071): 116.7755674348658, (28, 3080): 158.58201221870704, (28, 3199): 134.59088108918132, (28, 3200): 134.22941070641286, (28, 3205): 141.23028746843391, (28, 3209): 135.02023621186484, (28, 3215): 133.5860260452544, (28, 3217): 132.27144276324177, (28, 3249): 132.95480576605277, (28, 3263): 143.10698019934182, (28, 3289): 134.2231355080945, (28, 3301): 136.341592235389, (28, 3302): 135.18528348930883, (28, 3307): 134.3791406049707, (28, 3310): 136.9347724123656, (28, 3391): 176.27424801862193, (28, 3509): 215.82038613375684, (28, 3510): 217.168734457563, (28, 3511): 216.04383089486922, (28, 3512): 216.6877465046885, (28, 3514): 216.23435393893527, (28, 3519): 213.90037631762473, (28, 3536): 213.0402865973823, (28, 3545): 210.6961614079032, (28, 3548): 212.4961366072155, (28, 3572): 212.5498681945823, (28, 3581): 214.98808590152143, (28, 3583): 214.92595499957417, (28, 3601): 211.82996406985612, (28, 3656): 215.11774977466953, (28, 3669): 220.42578514724383, (28, 3670): 219.38980017030158, (28, 3695): 224.879057759642, (28, 3696): 223.90347201760076, (28, 3782): 209.55388377116824, (28, 3792): 211.2984848583654, (28, 3989): 805.2596629345725, (28, 4008): 812.4579063926517, (28, 4031): 811.3291252760458, (28, 4045): 809.405220408557, (28, 4144): 810.4009505441392, (28, 4145): 803.8008411003842, (28, 4164): 807.7699670025589, (28, 4168): 805.8189943330575, (28, 4173): 805.5063148506121, (28, 4181): 801.1066459183161, (28, 4228): 796.2823595412005, (28, 4248): 795.3705494437575, (28, 4254): 758.0707776358173, (28, 4260): 758.0069884560576, (28, 4262): 760.7078817422249, (28, 4273): 760.0138211350428, (28, 4319): 736.6101201262085, (28, 4326): 735.7686869309282, (28, 4328): 736.0476591116893, (28, 4334): 737.6843337565656, (28, 4335): 737.1236343195582, (28, 4372): 694.5244621345603, (28, 4413): 715.0673514511933, (28, 4434): 694.0003227057946, (28, 4447): 698.0749357489193, (28, 4452): 694.1174135039604, (28, 4463): 641.2724408225082, (28, 4465): 643.2985340426849, (28, 4619): 713.658736125807, (28, 4645): 719.5185473651609, (28, 4657): 718.1780799768273, (28, 4666): 715.6827742999868, (28, 4676): 719.351895826105, (28, 4678): 720.4158958257814, (28, 4689): 717.2989937674013, (28, 4704): 735.42566016278, (28, 4726): 767.5108059677553, (28, 4727): 766.8658582123941, (28, 4730): 765.6569729949075, (28, 4731): 765.7286690196744, (28, 4734): 768.005348755531, (28, 4735): 767.1577611284525, (28, 4736): 767.2608206929677, (28, 4737): 765.8968602937134, (28, 4738): 765.8756035646539, (28, 4756): 766.394426408184, (28, 4760): 764.3168201522366, (28, 4761): 765.1472084315112, (28, 4762): 763.1523393235841, (28, 4765): 764.4952304261733, (28, 4773): 769.0116378162152, (28, 4774): 768.0331730219067, (28, 4790): 768.6430668423083, (28, 4795): 768.1801161976007, (28, 4799): 768.0989427900892, (28, 4801): 768.8996659035137, (28, 4804): 768.9027919227414, (28, 4805): 768.516375647099, (28, 4806): 767.1941872888164, (28, 4815): 766.2211417135968, (28, 4816): 768.0214272400025, (28, 4817): 767.8770712537713, (28, 4826): 767.0567647877907, (28, 4830): 765.9416201890971, (28, 4839): 766.1732257882812, (28, 4840): 766.5514397487772, (28, 4841): 765.0311095488819, (28, 4846): 764.6618143969132, (28, 4848): 764.1172689451929, (28, 4850): 764.6356874862469, (28, 4871): 758.9734661542839, (28, 4883): 764.1686238904189, (28, 4900): 762.0533283837386, (28, 4901): 760.934876511456, (28, 4917): 705.6005347252832, (28, 4931): 700.4358500771724, (28, 4944): 706.4888449369413, (28, 4956): 701.0803016782053, (28, 4958): 700.3322928205562, (28, 4959): 698.9414409491919, (28, 4961): 702.3704635406697, (28, 4966): 699.4713023660248, (28, 5207): 693.6890714290496, (28, 5272): 615.4936401217205, (28, 5283): 617.1350076188063, (28, 5287): 618.3628579940113, (28, 5289): 619.0322727330572, (28, 5293): 617.1622488944728, (28, 5295): 621.9567916560607, (28, 5296): 621.0728670664442, (28, 5298): 620.5417938784276, (28, 5303): 621.2327508395289, (28, 5305): 612.8480385346478, (28, 5306): 610.308275579727, (28, 5307): 611.8903487080903, (28, 5308): 613.3538386848386, (28, 5313): 614.3593077737477, (28, 5314): 615.7577837070961, (28, 5317): 612.8064661009902, (28, 5319): 619.3737437228149, (28, 5324): 619.0567325228811, (28, 5326): 618.9030512711106, (28, 5348): 609.1745474751011, (28, 5351): 609.2361000508273, (28, 5399): 618.7579452569655, (28, 5413): 609.5197110912048, (28, 5422): 620.533205103028, (28, 5445): 616.2213286456197, (28, 5448): 614.5697589805501, (28, 5456): 613.2764458642265, (28, 5467): 614.5711446615334, (28, 5624): 599.4040313650729, (28, 5671): 664.471932506148, (28, 5672): 662.2969679378206, (28, 5797): 691.1726898427778, (28, 5871): 634.2375098880365, (28, 5976): 614.0901997287739, (28, 6118): 153.76003696005083, (28, 6248): 183.32507446158021, (28, 6345): 532.146430327061, (28, 6352): 526.1833378876328, (28, 6354): 533.4683500869409, (28, 6359): 534.8946130097675, (28, 6376): 527.7603863368278, (28, 6378): 532.7878721382702, (28, 6381): 534.5789403339919, (28, 6383): 530.7802789488577, (28, 6396): 534.9201181629613, (28, 6399): 532.524289625807, (28, 6408): 526.1435882995872, (28, 6409): 528.3034293283491, (28, 6419): 517.6300593114825, (28, 6422): 526.4091251645631, (28, 6423): 525.8901913025726, (28, 6424): 532.1685881907217, (28, 6439): 530.8178154955027, (28, 6464): 528.9622849985582, (28, 6465): 528.5747100236986, (28, 6469): 529.7803139194106, (28, 6470): 529.5209253438195, (28, 6472): 537.0159100234213, (28, 6480): 534.7328274833629, (28, 6486): 537.3162822004581, (28, 6497): 536.3882363595338, (28, 6503): 528.211121010286, (28, 6508): 529.242051570913, (28, 6509): 530.1343864019902, (28, 6521): 535.047197489987, (28, 6544): 534.0540697518421, (28, 6552): 526.3547023650318, (28, 6553): 525.3542575265368, (28, 6554): 524.34439039962, (28, 6578): 528.1141339139347, (28, 6582): 526.7720424529467, (28, 6601): 528.4386789368701, (28, 6609): 536.9988793977946, (28, 6610): 537.1462133964732, (28, 6611): 537.6836120664225, (28, 6614): 537.3820406659621, (28, 6615): 537.4406418978807, (28, 6616): 538.0169270854994, (28, 6617): 537.7237756617124, (28, 6618): 538.7278903983905, (28, 6619): 536.5995083552674, (28, 6620): 537.8295753136323, (28, 6621): 536.9522597715742, (28, 6622): 537.2915975403329, (28, 6623): 537.0559348975349, (28, 6624): 536.0888512034845, (28, 6625): 536.0472666200338, (28, 6626): 536.6483914855531, (28, 6627): 537.3690638164725, (28, 6628): 537.4470136737456, (28, 6629): 536.0619903604281, (28, 6630): 535.677287452903, (28, 6632): 536.0928871628902, (28, 6634): 534.6360980232201, (28, 6635): 536.7643131690536, (28, 6636): 537.9913334889598, (28, 6637): 534.8918921682703, (28, 6638): 535.5718760058579, (28, 6639): 537.3267286790249, (28, 6640): 535.8220563163895, (28, 6641): 536.7697796752573, (28, 6642): 535.4478056788286, (28, 6643): 536.7107809830419, (28, 6645): 536.6175231068024, (28, 6646): 538.5901497098951, (28, 6647): 535.7788312010507, (28, 6653): 537.4697907979255, (28, 6655): 537.4076887560263, (28, 6658): 534.4892329603731, (28, 6662): 535.2470345786622, (28, 6819): 484.692598873101, (28, 6996): 498.6593553277786, (28, 7059): 510.0909971822953, (28, 7187): 488.0339773901977, (28, 7304): 464.6331983011264, (28, 7528): 496.21520899743575, (28, 7720): 565.2873197623308, (28, 7793): 563.449788906169, (28, 7807): 564.5176972937508, (28, 7808): 563.0212187392738, (28, 7831): 541.7408111628685, (28, 7850): 553.4327088718001, (28, 7852): 551.2437382613009, (28, 8012): 562.8127758047596, (28, 8125): 570.0139985374834, (28, 8208): 586.2059202957803, (28, 8392): 547.5834437373745, (28, 8651): 430.08810683681247, (28, 9088): 485.2820279801554, (28, 9443): 397.2345816070276, (28, 9444): 398.85970108880105, (28, 9828): 346.99402043032063, (28, 9868): 345.02627189805037, (28, 10180): 571.0433011571457, (28, 10256): 600.4252830174139, (28, 10276): 587.0400408018054, (28, 10378): 591.4889960817395, (28, 10676): 560.7113817746264, (28, 10714): 541.3221680993088, (28, 10730): 545.0577228725763, (28, 10862): 530.2447444846521, (28, 10881): 534.8387259499683, (28, 10883): 534.1930483731867, (28, 10885): 529.2917854110735, (28, 10891): 533.193922362453, (28, 10909): 533.1147464401062, (28, 10911): 534.0937349053193, (28, 10913): 532.9253773014925, (28, 10915): 533.0506375731132, (28, 10919): 533.8352395005226, (28, 11037): 498.9888405927685, (28, 11039): 488.7616460399917, (28, 11516): 874.4037970954695, (28, 11856): 738.3998008817333, (28, 11857): 737.2795722915467, (28, 11861): 737.8798872045953, (28, 11881): 736.6704586720715, (28, 11902): 731.5710037124963, (28, 11911): 730.6747437776907, (28, 11914): 731.3718250168702, (28, 11922): 735.1516712806016, (28, 11924): 736.3606189584252, (28, 11926): 734.8933523049092, (28, 11950): 737.8173442832125, (28, 11963): 742.6121911549324, (28, 11983): 739.3546875184425, (28, 11985): 745.0166578228391, (28, 12009): 744.0739690408594, (28, 12010): 740.6747768579955, (28, 12018): 741.2339438192181, (28, 12020): 742.1591387217691, (28, 12021): 742.7215299378742, (28, 12024): 745.9735950389819, (28, 12025): 744.876331925334, (28, 12027): 744.1058532369503, (28, 12031): 740.1056613977336, (28, 12032): 741.2386715464423, (28, 12035): 743.8537746436048, (28, 12041): 745.423942914348, (28, 12045): 700.2059476021456, (28, 12145): 721.0384375957702, (28, 12275): 807.170320903236, (28, 12294): 798.2178693554812, (28, 12358): 825.0320689192238, (28, 12463): 835.2941727786034, (28, 12465): 834.9706829932696, (28, 12482): 839.7228891908784, (28, 12503): 839.0448351826377, (28, 12506): 840.2977285994507, (28, 12549): 837.7636844996903, (28, 12559): 836.7732698244379, (28, 12569): 837.737373331249, (28, 12572): 838.6830023470898, (28, 12574): 836.7264370983627, (28, 12576): 838.8732525152783, (28, 12591): 838.7449252831171, (28, 12608): 846.4217469755134, (28, 12696): 834.2924621580509, (28, 12710): 841.5367144174461, (28, 12728): 837.9355519339846, (28, 12766): 632.8939330363686, (28, 12771): 623.6952151829087, (28, 12790): 622.4433891421024, (28, 12795): 619.5548313618204, (28, 12797): 607.6317273593539, (28, 12798): 609.280031168622, (28, 12811): 618.8284162782875, (28, 12830): 615.6061032708977, (28, 12848): 617.3179750885914, (28, 12850): 618.1532214895952, (28, 12852): 615.1652187230007, (28, 12854): 613.6997633385463, (28, 12859): 618.7889115298743, (28, 12861): 610.9126005357596, (28, 12865): 620.6079022135234, (28, 12866): 619.8665032682119, (28, 12867): 622.7903498232516, (28, 12874): 621.3703063235114, (28, 12875): 622.4843197655401, (28, 12881): 617.9239114276105, (28, 12883): 619.7375297668999, (28, 12885): 623.4436943049874, (28, 12888): 618.9054186508082, (28, 12889): 618.504184338471, (28, 12892): 621.6800711103995, (28, 12893): 618.9639033943647, (28, 12896): 619.8454347907237, (28, 12906): 621.4377454588713, (28, 13018): 608.3852336930206, (28, 13071): 608.6179239601948, (28, 13131): 596.6472079791422, (28, 13146): 606.2600542649583, (28, 13159): 593.3502707477048, (28, 13193): 594.7609723409713, (28, 13198): 577.764889489653, (28, 13292): 597.193496872908, (28, 13296): 602.7177658893205, (28, 13406): 567.466420468085, (28, 13407): 566.9425194617814, (28, 13417): 565.9501014371912, (28, 13418): 567.8263738778678, (28, 13438): 574.9940843237338, (28, 13442): 576.3767310676766, (28, 13443): 574.9638455399516, (28, 13764): 458.74469114860256, (28, 13766): 460.5064740657513, (28, 13771): 459.36989306921714, (28, 13783): 456.32770289214164, (28, 13784): 462.18342685788537, (28, 13792): 456.89243189823503, (28, 13824): 455.22729868352104, (28, 14017): 462.7260779005394, (28, 14870): 537.3405033929263, (28, 14997): 479.4802870450919, (28, 15000): 479.81885934063024, (28, 15003): 481.2220735173781, (28, 15006): 483.32133974504166, (28, 15007): 484.5871545190265, (28, 15056): 484.8759874858856, (28, 15063): 483.8521869633499, (28, 15069): 483.6243110670025, (28, 15076): 484.8862703476667, (28, 15086): 480.77799188099766, (28, 15087): 479.6222258071903, (28, 15111): 475.7261269702147, (28, 15116): 477.9761517518857, (28, 15722): 444.74179026193013, (28, 15998): 427.29801793264124, (28, 16073): 263.9538812504433, (28, 16939): 24.0, (28, 16940): 24.0, (28, 16951): 24.0, (28, 16963): 24.0, (28, 16965): 24.0, (28, 16969): 24.0, (28, 16970): 24.0, (28, 16971): 24.0, (28, 16973): 24.0, (28, 16974): 24.0, (28, 16976): 24.0, (28, 16978): 24.0, (28, 16980): 24.0, (28, 16982): 24.0, (28, 17045): 121.01577413447444, (28, 17048): 122.56312832460354, (28, 17304): 785.5963688400466, (28, 17305): 784.0742698898883, (28, 17330): 785.353631697545, (28, 17334): 783.1910819590322, (28, 17343): 787.1384582542977, (28, 17345): 782.8252961401107, (28, 17347): 785.0015861874132, (28, 17351): 779.8612575002713, (28, 17372): 782.8139829018431, (28, 17373): 787.0368366139511, (28, 17377): 787.3105188529967, (28, 17382): 784.5024008183626, (28, 17383): 785.1172449562147, (28, 17389): 783.4372016197239, (28, 17400): 786.3416029716848, (28, 17401): 786.329290307516, (28, 17402): 786.4810963382382, (28, 17403): 786.7386955362336, (28, 17440): 782.691413160668, (28, 17455): 786.4618832069287, (28, 17491): 786.5196310099407, (28, 17507): 782.11762069181, (28, 17509): 783.7583121920499, (28, 17590): 778.4987921698942, (28, 17615): 771.4402683701531, (28, 17642): 772.8963483570896, (28, 17643): 772.6620821044368, (28, 17668): 771.4362645771276, (28, 17721): 768.2402736926985, (28, 17754): 783.2839414966053, (28, 17769): 782.9346340613706, (28, 17776): 776.1783454572638, (28, 17804): 785.5444035760019, (28, 17809): 787.1302119956762, (28, 17824): 786.2575382735981, (28, 17837): 780.8852008088454, (28, 17838): 780.903574955422, (28, 17862): 779.6508933292473, (28, 17866): 783.0971390833977, (28, 17872): 778.6075618092334, (28, 17873): 775.9399033434214, (28, 17881): 780.0098408925284, (28, 17947): 169.66233686413864, (28, 17951): 171.6484109791602, (28, 17953): 172.65593015055936, (28, 17954): 172.9259569724063, (28, 17959): 168.97712558007498, (28, 17963): 168.62521046848659, (28, 18000): 181.45676602507314, (28, 18001): 181.6804727647132, (28, 18111): 192.4607741508706, (28, 18148): 240.61305503069923, (28, 18166): 223.19687227863264, (28, 18189): 201.10976632577515, (28, 18239): 787.9471720647346, (28, 18240): 787.8878324703317, (28, 18245): 788.0744549212602, (28, 18247): 787.68438174892, (28, 18251): 788.0191735585904, (28, 18256): 788.3347279886876, (28, 18258): 787.913362456282, (28, 18259): 787.9630691213176, (28, 18260): 788.0867874864203, (28, 18262): 788.3520484924817, (28, 18263): 788.4159015255758, (28, 18264): 788.5415876874953, (28, 18266): 788.4335217736839, (28, 18267): 788.562175423121, (28, 18268): 788.6100797626428, (28, 18269): 788.8620096308003, (28, 18275): 788.7429753043654, (28, 18285): 788.5149370388525, (28, 18308): 785.852980907913, (28, 18313): 784.8363870734493, (28, 18314): 785.1757782240205, (28, 18315): 788.9627453084863, (28, 18316): 788.8854792250355, (28, 18317): 788.9998661754811, (28, 18320): 789.1873611429395, (28, 18321): 789.2253972083539, (28, 18322): 789.416842201247, (28, 18324): 789.6514881905741, (28, 18325): 790.3235726214589, (28, 18326): 790.0757099099695, (28, 18327): 789.0583911270975, (28, 18329): 790.68687245733, (28, 18330): 790.1793866298718, (28, 18331): 789.7567891347456, (28, 18332): 789.2929724321604, (28, 18333): 790.1584505871257, (28, 18336): 789.8636461221917, (28, 18337): 790.1270466184571, (28, 18403): 789.4761915367884, (28, 18432): 778.6566039797432, (28, 18451): 785.990154621243, (28, 18466): 793.2366166451249, (28, 18481): 789.2817549088024, (28, 18483): 789.2435800122028, (28, 18484): 788.9027257236892, (28, 18485): 787.9138095700101, (28, 18486): 789.037764276001, (28, 18487): 788.2212982858047, (28, 18489): 788.8094851115834, (28, 18490): 789.7686264176068, (28, 18491): 790.1738678274005, (28, 18492): 787.3247402336973, (28, 18493): 788.9372534465091, (28, 18494): 788.6148263295204, (28, 18495): 789.4721517235866, (28, 18496): 789.0172692836816, (28, 18497): 788.0667570596323, (28, 18498): 788.1162358997761, (28, 18499): 788.7336284222662, (28, 18501): 788.3513057057904, (28, 18502): 787.960356289566, (28, 18503): 787.6161051158431, (28, 18504): 789.1396942138574, (28, 18506): 788.5144222740819, (28, 18507): 788.1618952889645, (28, 18508): 788.6831120082529, (28, 18509): 788.7255727221881, (28, 18510): 787.6769144610504, (28, 18511): 789.1302151311022, (28, 18512): 788.5946542632613, (28, 18515): 789.229139435141, (28, 18516): 789.3796134269173, (28, 18517): 788.9371685303449, (28, 18518): 789.6743933555521, (28, 18519): 789.2040138670881, (28, 18520): 788.5226235679314, (28, 18522): 790.8140259252236, (28, 18523): 790.940823402809, (28, 18532): 791.5509014734777, (28, 18535): 790.3243962692978, (28, 18537): 789.6414851823603, (28, 18539): 789.805040598193, (28, 18540): 789.906426919638, (28, 18541): 790.2606149441784, (28, 18542): 790.4817089921335, (28, 18543): 789.3994552659155, (28, 18546): 789.9804076249447, (28, 18555): 791.0543581907442, (28, 18556): 791.2763141878122, (28, 18565): 791.5243857795466, (28, 18567): 791.9145908593528, (28, 18568): 791.2964022625939, (28, 18577): 795.4799458412826, (28, 18583): 794.6716003134467, (28, 18605): 795.4226810415806, (28, 18608): 792.428163739081, (28, 18616): 799.3367040247789, (28, 18618): 802.7333761436494, (28, 18625): 801.3144425565134, (28, 18645): 798.2540885464955, (28, 18646): 799.115898104026, (28, 18653): 796.6064843132592, (28, 18654): 799.2973637301883, (28, 18655): 797.5862089554208, (28, 18666): 807.935372707528, (28, 18837): 791.4892386864428, (28, 18974): 784.9867356697104, (28, 18999): 787.2835182779521, (28, 19000): 788.2817847299297, (28, 19174): 738.4394290095681, (28, 19342): 758.0392990893455, (28, 19455): 747.5321414946068, (28, 19555): 697.6415620797226, (28, 19564): 700.2428433309, (28, 19573): 698.1869937490966, (28, 19586): 697.2916874364192, (28, 19605): 698.1434084305344, (28, 19611): 699.5459630651138, (28, 19614): 699.0014254725477, (28, 19641): 722.8636233130527, (28, 19702): 722.3363349707714, (28, 19713): 720.6130130589308, (28, 19731): 689.9826102498332, (28, 19819): 739.7224688759962, (28, 19893): 684.6480495835144, (28, 19899): 694.8155446672122, (28, 19929): 687.5602386630901, (28, 19951): 708.6807320478032, (28, 19962): 688.8231729589911, (28, 19970): 694.4066053429816, (28, 19971): 694.2870265911253, (28, 19972): 692.3465228807306, (28, 19975): 691.6601296790235, (28, 19978): 714.191832564822, (28, 19987): 714.7127659907432, (28, 19989): 708.8709598387526, (28, 20039): 715.8638445585269, (28, 20043): 718.524396571965, (28, 20047): 716.8464943061258, (28, 20052): 710.2037400116861, (28, 20054): 710.6103728166144, (28, 20085): 741.4471540768546, (28, 20104): 743.3351704980427, (28, 20132): 731.5536431757447, (28, 20203): 681.404122382202, (28, 20280): 678.2956813596101, (28, 20285): 677.3866159218072, (28, 20290): 679.462428801513, (28, 20297): 677.5238648515211, (28, 20309): 714.0194768191079, (28, 20453): 746.278546300965, (28, 20485): 665.2585291109782, (28, 20520): 660.3794760725588, (28, 20526): 657.7403780346542, (28, 20698): 422.94254030035574, (28, 20868): 368.52480018698054, (28, 21042): 618.9939976237797, (28, 21057): 632.0672182143473, (28, 21066): 625.632491110386, (28, 21075): 623.2135331596932, (28, 21093): 619.9424288588821, (28, 21098): 629.173968469868, (28, 21127): 620.0505970657299, (28, 21130): 622.4998264029254, (28, 21144): 622.1629130531409, (28, 21146): 619.1965337905135, (28, 21147): 621.9550925503803, (28, 21148): 624.2115082805491, (28, 21153): 618.9584169539714, (28, 21293): 640.5968832708293, (28, 21426): 637.6589957246281, (28, 21442): 651.6187665671895, (28, 21451): 652.9626196069067, (28, 21466): 644.5814034985577, (28, 21469): 646.6310344664583, (28, 21471): 643.5427631302649, (28, 21473): 645.2326180682387, (28, 21475): 643.7160299822293, (28, 21482): 647.9397994018793, (28, 21484): 647.505653508233, (28, 21488): 646.3078153928931, (28, 21494): 643.6835043722355, (28, 21498): 645.2162449303344, (28, 21500): 642.7748904436086, (28, 21514): 646.8390199690224, (28, 21537): 642.2932787974975, (28, 21662): 648.632916166969, (28, 21691): 640.5663431276153, (28, 21757): 626.3520602991282, (28, 21777): 593.656252708169, (28, 21778): 591.6222739071171, (28, 21779): 592.7339502992444, (28, 21790): 595.973454532301, (28, 21802): 595.8172064298759, (28, 21824): 597.9071113275849, (28, 21874): 593.2322910721028, (28, 21879): 591.9912511445752, (28, 21983): 600.8264033937469, (28, 22002): 622.5731765583843, (28, 22132): 609.4401085954136, (28, 22261): 344.5011461680582, (28, 22298): 349.95393876825057, (28, 22339): 333.77221944623653, (28, 22508): 380.7461535430912, (28, 22841): 269.1979362771227, (28, 22842): 268.29784414379094, (28, 22874): 262.756162717936, (28, 22941): 266.0967279224123, (28, 22956): 266.7924892594946, (28, 22960): 269.4066031485496, (28, 22968): 258.5608125480187, (28, 22970): 260.7574959978198, (28, 22974): 253.80572607974665, (28, 22980): 255.63829958526517, (28, 23025): 244.44065651246777, (28, 23028): 241.75000368208038, (28, 23081): 231.5845365804453, (28, 23104): 209.6227128161957, (28, 23147): 225.2485143089069, (28, 23298): 682.0850267618958, (28, 23376): 676.2505791999896, (28, 23381): 672.7367888507925, (28, 23529): 685.7917043552771, (28, 23556): 682.4206480831067, (28, 23718): 678.5197374782982, (28, 24001): 716.605885482849, (28, 24094): 727.429875654683, (28, 24129): 733.2137475681915, (28, 24174): 721.2356015752781, (28, 24235): 734.1111728099074, (28, 24259): 739.6062359000151, (28, 24260): 739.1967330344833, (28, 24261): 737.9521749897382, (28, 24305): 746.187761018002, (28, 24306): 747.3116420968855, (28, 24307): 745.6240604058356, (28, 24308): 730.9128791749662, (28, 24498): 760.624843709228, (28, 24499): 760.7552755637904, (28, 24500): 759.6834854000305, (28, 24668): 752.1993359966821, (28, 24711): 767.9699420498647, (28, 24756): 772.0085307719094, (28, 24788): 773.5866783533962, (28, 24809): 767.3588728663294, (28, 24813): 769.2830671923294, (28, 24821): 768.6412190248708, (28, 24825): 769.1593879164024, (28, 24832): 766.9028808345511, (28, 24833): 767.8777580595928, (28, 24835): 768.8618837832879, (28, 24837): 770.381802016646, (28, 24840): 766.7679867047588, (28, 24841): 768.240976139989, (28, 24844): 766.8341907157674, (28, 24845): 767.6367457504615, (28, 24846): 767.6726490690314, (28, 24849): 768.2144844074438, (28, 24850): 769.6075736584697, (28, 24863): 755.8894216378989, (28, 24866): 757.6240334070961, (28, 24885): 759.7636218898548, (28, 24886): 759.9627627748293, (28, 24889): 763.6032984952191, (28, 24903): 764.9995601402019, (28, 24909): 758.5270563202782, (28, 24999): 832.8069983639269, (28, 25019): 830.5384014823345, (28, 25028): 831.8508535875845, (28, 25137): 679.705622436686, (28, 25145): 681.9875934330038, (28, 25208): 705.9902929577744, (28, 25233): 702.8321119786066, (28, 25371): 681.3096356277357, (28, 25377): 675.268221410995, (28, 25828): 560.4296513670616, (28, 25851): 543.663632739236, (28, 25874): 560.022344436312, (28, 25898): 566.8766107400604, (28, 25946): 558.6854405274958, (28, 26047): 594.0477079973459, (28, 26066): 638.1398551425384, (28, 26197): 610.1554738445213, (28, 26212): 502.91061625895856, (28, 26253): 497.21713749431177, (28, 26254): 499.31453441173903, (28, 26257): 501.53539781031293, (28, 26258): 498.4277899124831, (28, 26260): 500.0081774257982, (28, 26266): 497.31025300177635, (28, 26267): 499.2645120847088, (28, 26271): 499.3928780891272, (28, 26304): 519.3796322844229, (28, 26305): 519.0612560212729, (28, 26363): 554.088971404472, (28, 26441): 374.610297770884, (28, 26442): 374.3798647239067, (28, 26450): 376.9386923439035, (28, 26459): 380.14011639178585, (28, 26462): 381.12842438946194, (28, 26467): 374.30781068914797, (28, 26471): 374.65033091683404, (28, 26472): 374.39943808186376, (28, 26473): 374.04022555962587, (28, 26476): 370.6841780289594, (28, 26485): 377.4601669366304, (28, 26493): 375.838294379602, (28, 26524): 381.46176886032646, (28, 26525): 380.8937464127586, (28, 26556): 375.72466378287663, (28, 26560): 378.51944223837035, (28, 26561): 380.5858901335214, (28, 26564): 375.66130271834817, (28, 26569): 380.09767360432244, (28, 26570): 379.7122690029638, (28, 26573): 377.97447940995227, (28, 26581): 376.82357376599674, (28, 26583): 378.08656437536473, (28, 26593): 375.28832645396824, (28, 26837): 372.5916044193726, (28, 26844): 371.62402362034084, (28, 26863): 370.77250700205803, (28, 26893): 366.6702735580392, (28, 26902): 365.2341066142203, (28, 26905): 369.3917476097986, (28, 26912): 367.42235887247085, (28, 26921): 368.98459891922613, (28, 26922): 367.82030017005235, (28, 27212): 432.92089473356464, (28, 27218): 436.9268569658388, (28, 27239): 430.77113996417023, (28, 27257): 430.4649778733408, (28, 27274): 429.8550485043157, (28, 27279): 428.8203907533739, (28, 27282): 429.77749897328425, (28, 27283): 431.7145442882935, (28, 27285): 428.7112773653436, (28, 27286): 427.4975358163304, (28, 27290): 430.4098210058795, (28, 27295): 432.7741258820624, (28, 27300): 430.1656066229992, (28, 27344): 427.391479241073, (28, 27366): 425.11389608702143, (28, 27383): 426.1182645321577, (28, 27398): 427.90389159606644, (28, 27406): 429.70399804483935, (28, 27407): 430.3937345627692, (28, 27426): 439.74012931245875, (28, 27432): 441.25049977366274, (28, 27460): 441.3684466984911, (28, 27523): 406.4724540161881, (28, 27545): 411.69233786906983, (28, 27602): 386.7143621611581, (28, 27606): 388.12819108913374, (28, 27646): 382.7281698631117, (28, 27667): 377.43966873229516, (28, 27672): 378.12580511225565, (28, 27674): 378.4147343391628, (28, 27688): 381.45283283948766, (28, 27692): 376.137053872228, (28, 27693): 376.7095615327923, (28, 27705): 375.6619117542674, (28, 27712): 374.4579289418924, (28, 27786): 427.77686830902843, (28, 27790): 443.32454625224597, (28, 27791): 445.48562183265443, (28, 27795): 427.20056641822424, (28, 27801): 437.49342687950224, (28, 27813): 425.7777846385786, (28, 27816): 429.05911401127634, (28, 27823): 438.01005312318665, (28, 27830): 432.8599548472961, (28, 27884): 381.54022003410154, (28, 27885): 383.35974401079244, (28, 27896): 382.70174842434295, (28, 27919): 383.6520386581498, (28, 27922): 382.3927262395921, (28, 27930): 383.02930970825025, (28, 27934): 382.20481400670855, (28, 27935): 381.23734816991674, (28, 27948): 335.9256002074922, (28, 27951): 351.9047191614392, (28, 28061): 263.698850613754, (28, 28290): 208.80739196421573, (28, 28292): 203.41212637398266, (28, 28293): 207.3902969274054, (28, 28295): 204.83525810384654, (28, 28296): 207.29098278300737, (28, 28297): 211.35050322405095, (28, 28302): 209.01538508237326, (28, 28310): 130.3878586420559, (28, 28313): 134.52242978672325, (28, 28372): 124.30616435497159, (28, 28398): 124.91770832096604, (28, 28399): 126.04602721331055, (28, 28400): 125.50533215444908, (28, 28401): 125.73523129754409, (28, 28445): 138.29169678300576, (28, 28475): 120.44323904952809, (28, 28885): 732.6888225436134, (28, 28886): 731.5102038959426, (28, 28915): 732.1272548699505, (28, 28916): 731.3050458068517, (28, 28917): 730.6383531086269, (28, 28921): 734.8016693953928, (28, 28931): 734.417853560842, (28, 28945): 727.856422948192, (28, 28982): 729.5629006890554, (28, 29219): 733.9321037229926, (28, 29228): 729.1092675051498, (28, 29246): 759.4136475511772, (28, 29248): 758.6002865880474, (28, 29282): 752.2289037288709, (28, 29290): 762.9648440657608, (28, 29291): 761.567204813462, (28, 29292): 762.8227740917289, (28, 29293): 760.3119806726141, (28, 29294): 762.1514217102588, (28, 29298): 760.4038132252654, (28, 29299): 760.0888688004595, (28, 29304): 757.9633761065226, (28, 29317): 752.0662323161707, (28, 29323): 751.6193500200472, (28, 29330): 754.4436782982327, (28, 29331): 755.9289055573092, (28, 29344): 733.7375026611642, (28, 29445): 676.8006989228909, (28, 29724): 301.8540877274844, (28, 29738): 302.1977873903337, (28, 29745): 302.5889119475951, (28, 29748): 309.8176749548122, (28, 29750): 313.33101328003113, (28, 29759): 308.49441682758936, (28, 29772): 309.858406825838, (28, 29781): 309.75981727245215, (28, 29784): 306.50961414147804, (28, 29790): 311.29620280434955, (28, 29811): 313.6360541233419, (28, 29817): 334.4581488483639, (28, 29818): 334.4796756236577, (28, 29929): 298.0839612456365, (28, 30039): 283.39749635606603, (28, 30066): 269.04249552485356, (28, 30116): 273.25227912006335, (28, 30238): 284.74798471013986, (28, 30248): 257.6764925504642, (28, 30260): 255.74363444859105, (28, 30545): 716.8272522392422, (28, 30733): 664.7248853565033, (28, 30756): 649.9794959769578, (28, 30921): 675.6834115198235, (28, 31079): 542.5248689595152, (28, 31149): 536.0829064875238, (28, 31154): 536.115832361445, (28, 31160): 535.6920756913009, (28, 31163): 535.288193212976, (28, 31189): 513.7373889440671, (28, 31215): 514.8954612216637, (28, 31259): 511.68384126512996, (28, 31262): 509.38196774862433, (28, 31430): 544.4686352240665, (28, 31568): 482.6311554265033, (28, 31751): 530.4919288923837, (29, 109): 111.84245627439465, (29, 872): 531.8379518862429, (29, 873): 534.3332738707801, (29, 877): 533.4860522058609, (29, 879): 533.8649456008826, (29, 884): 531.5583894637728, (29, 889): 533.0798096892214, (29, 891): 530.7082612148944, (29, 892): 535.7810264349096, (29, 894): 535.4294477869481, (29, 896): 532.8783385047676, (29, 903): 533.6820118020659, (29, 909): 529.1422380499519, (29, 910): 530.0603783552986, (29, 912): 528.4293032091232, (29, 913): 526.6617823698218, (29, 916): 525.7960360790398, (29, 926): 530.773053098263, (29, 927): 529.9176203600671, (29, 948): 529.7890258297062, (29, 961): 530.8722834234497, (29, 962): 531.0989123578202, (29, 963): 531.3720259491745, (29, 967): 534.7007539558268, (29, 974): 533.5723995279811, (29, 998): 535.7623736432157, (29, 1014): 589.2117899535046, (29, 1086): 523.5006462920461, (29, 1087): 522.9346341139318, (29, 1089): 520.7699809389887, (29, 1090): 521.8397956337642, (29, 1092): 525.4277816136299, (29, 1097): 522.7411183436535, (29, 1107): 527.0540820675286, (29, 1387): 151.12729809830307, (29, 1554): 112.875337407494, (29, 1827): 647.7670141561323, (29, 1828): 647.990841386343, (29, 1829): 648.4027400899441, (29, 1830): 648.203187619669, (29, 1831): 648.3923546808625, (29, 1832): 648.104142374865, (29, 1833): 648.1005900203853, (29, 1836): 647.7743678814531, (29, 1841): 649.426358836457, (29, 1843): 648.7549706531084, (29, 1844): 649.0873871340219, (29, 1845): 648.3174798982274, (29, 1847): 645.6308515876377, (29, 1848): 646.5340256741127, (29, 1849): 650.8005024479546, (29, 1850): 651.2125983882985, (29, 1851): 647.3150591092759, (29, 1852): 647.45918473673, (29, 1854): 647.8298814601227, (29, 1856): 645.6055663237634, (29, 1857): 646.5148694168362, (29, 1858): 650.334899806452, (29, 1861): 648.4126826231344, (29, 1866): 645.6155821775541, (29, 1867): 649.4069793382455, (29, 1868): 648.8044905714941, (29, 1870): 649.1141791615388, (29, 1871): 649.2198275245777, (29, 1875): 647.7313690859927, (29, 1880): 646.100244927335, (29, 1882): 646.4779835968851, (29, 1883): 651.1587489875241, (29, 1889): 646.4402245114854, (29, 1893): 648.3249870119749, (29, 1894): 647.6704993815481, (29, 1899): 645.8293391458345, (29, 1900): 646.2689513968278, (29, 1902): 649.4222606486659, (29, 1905): 650.2886677754899, (29, 1907): 647.0642363471509, (29, 1910): 647.269125111123, (29, 1917): 651.7530477261292, (29, 1920): 647.0569257169864, (29, 1935): 650.251272687521, (29, 1937): 650.9716040072244, (29, 1946): 644.2491309274163, (29, 1949): 644.9845832497763, (29, 1950): 642.4594412566742, (29, 1951): 643.7207554935302, (29, 1952): 644.9063545731999, (29, 1953): 645.145535083854, (29, 1954): 644.6644342152276, (29, 1958): 644.8484383394692, (29, 1960): 646.2144562605117, (29, 1968): 646.7530921447717, (29, 1969): 650.259967112893, (29, 1974): 649.3564015480879, (29, 1975): 649.3972744850519, (29, 1979): 647.434646119478, (29, 1980): 647.442613561055, (29, 1981): 647.8894448572976, (29, 1985): 648.2946624077497, (29, 1994): 641.7630098251515, (29, 2011): 646.498566079278, (29, 2019): 653.2324846971892, (29, 2020): 652.3430870717684, (29, 2029): 649.1215447132598, (29, 2030): 651.7241421721487, (29, 2032): 648.6754231674978, (29, 2033): 650.3079086991164, (29, 2034): 650.3567989116322, (29, 2036): 647.4379679005006, (29, 2037): 648.1719051103652, (29, 2038): 648.0812889595079, (29, 2042): 658.0836502076384, (29, 2050): 649.7433236051845, (29, 2051): 649.6835898122337, (29, 2053): 649.911897915815, (29, 2054): 650.7997475165145, (29, 2066): 649.0078573120944, (29, 2067): 648.9703161966793, (29, 2071): 640.0534576333872, (29, 2072): 641.6440322659868, (29, 2073): 636.89245835723, (29, 2074): 636.7219358801731, (29, 2080): 634.0665110949809, (29, 2082): 642.5207271305243, (29, 2083): 643.3381197999445, (29, 2089): 641.4679994214997, (29, 2090): 642.216189857845, (29, 2092): 641.0840151439786, (29, 2098): 635.0243389686244, (29, 2099): 636.0350612208865, (29, 2101): 634.9259264086637, (29, 2102): 639.3241261550153, (29, 2103): 637.9719202023529, (29, 2104): 637.2682294558296, (29, 2106): 643.9469771417816, (29, 2112): 635.581327028543, (29, 2113): 639.9967739149041, (29, 2114): 641.1884291651833, (29, 2117): 644.6749054613088, (29, 2123): 635.2978852226338, (29, 2124): 636.2052939340434, (29, 2134): 633.8115982928135, (29, 2138): 636.404516001686, (29, 2141): 634.06684465329, (29, 2148): 636.1495078815459, (29, 2150): 631.8940962892183, (29, 2151): 632.9040051050371, (29, 2152): 631.4433555150091, (29, 2153): 636.3829396755749, (29, 2154): 632.5759022677597, (29, 2155): 632.2724627558383, (29, 2156): 631.480365740794, (29, 2157): 632.9095306402488, (29, 2160): 638.0342442199591, (29, 2161): 631.3613069123203, (29, 2162): 636.8319681360455, (29, 2163): 635.5315177907579, (29, 2164): 635.4930808485642, (29, 2168): 632.6474690741052, (29, 2172): 633.8449647378949, (29, 2174): 632.8887233367957, (29, 2178): 634.6929875849067, (29, 2179): 634.1353320805979, (29, 2183): 636.428937499606, (29, 2185): 636.5324282558604, (29, 2186): 635.783515704813, (29, 2190): 638.1295916007074, (29, 2192): 636.7970218647838, (29, 2193): 636.65746023012, (29, 2194): 635.2967602253177, (29, 2195): 635.1993316528832, (29, 2197): 637.13778725298, (29, 2205): 635.3754244373087, (29, 2207): 633.0509877549138, (29, 2208): 634.3711194644574, (29, 2212): 636.8381652272367, (29, 2214): 611.1843792979298, (29, 2225): 614.7142418621064, (29, 2231): 606.2041353211332, (29, 2278): 628.8322959689095, (29, 2284): 631.7854842557482, (29, 2285): 631.4664019331909, (29, 2291): 626.4100444952089, (29, 2292): 626.4501102163912, (29, 2307): 629.9907363625288, (29, 2313): 625.9338415632049, (29, 2317): 624.1701507330016, (29, 2319): 627.4625592197546, (29, 2321): 628.8327823709028, (29, 2323): 628.5076641920933, (29, 2326): 633.0872214576268, (29, 2327): 631.88118787663, (29, 2329): 631.0739371817095, (29, 2330): 630.1907943296243, (29, 2332): 632.2503586930798, (29, 2344): 628.9526519924133, (29, 2346): 629.0039525054524, (29, 2361): 627.6491443466047, (29, 2368): 642.223297882478, (29, 2374): 643.6333674706342, (29, 2375): 644.0244242002453, (29, 2377): 639.3075929083165, (29, 2378): 644.9069855400459, (29, 2379): 645.1312080628238, (29, 2380): 645.513547380841, (29, 2383): 640.480981537696, (29, 2385): 641.160597922657, (29, 2395): 641.1463303012408, (29, 2397): 644.6276536236068, (29, 2398): 637.8167034987978, (29, 2399): 639.4394442998945, (29, 2400): 639.0623116777991, (29, 2402): 642.0146639111558, (29, 2403): 643.0612339956208, (29, 2404): 643.2871538484789, (29, 2405): 640.8042806099157, (29, 2407): 642.7637175343716, (29, 2408): 644.0370193782594, (29, 2409): 641.5407788838379, (29, 2411): 643.231135916409, (29, 2412): 642.8898398810904, (29, 2413): 643.7728511469719, (29, 2414): 642.4010770446448, (29, 2422): 642.9745372490355, (29, 2424): 643.1463474503126, (29, 2426): 643.3370299673601, (29, 2433): 641.4570658312759, (29, 2436): 641.0547752048158, (29, 2437): 634.917956739832, (29, 2440): 636.2388141983375, (29, 2445): 664.1969870750044, (29, 2447): 660.7764500922707, (29, 2454): 663.8969771862794, (29, 2455): 663.9852524982279, (29, 2460): 654.4087580255893, (29, 2461): 655.6094007993709, (29, 2471): 675.4091268910848, (29, 2492): 658.3676216837322, (29, 2511): 648.1007001636444, (29, 2523): 653.3631985106133, (29, 2525): 652.0951643444891, (29, 2535): 652.7962707302717, (29, 2537): 650.7151805649518, (29, 2538): 652.0676980225161, (29, 2539): 651.8579040097503, (29, 2540): 653.7508973479806, (29, 2542): 655.4018154052113, (29, 2559): 684.7644299418307, (29, 2575): 682.5142369384324, (29, 2599): 635.6692152289882, (29, 2600): 646.1700325209189, (29, 2607): 639.8025997298165, (29, 2627): 655.5876579423639, (29, 2647): 661.5351363076619, (29, 2674): 658.1570989842368, (29, 2681): 657.6022748280692, (29, 2683): 660.254338663555, (29, 2686): 656.9782981715538, (29, 2689): 693.9541807134475, (29, 2690): 694.1889814160958, (29, 2713): 703.0328282954745, (29, 2714): 703.8955756793064, (29, 2715): 704.788137917633, (29, 2739): 703.9242924017822, (29, 2740): 697.6153233244097, (29, 2741): 698.012042588751, (29, 2749): 702.9497652988829, (29, 2750): 703.1417127358562, (29, 2752): 703.7389107590396, (29, 2755): 704.5003906004272, (29, 2758): 704.3676946477311, (29, 2759): 704.3314705127212, (29, 2769): 703.194043157634, (29, 2771): 699.2333750433154, (29, 2779): 700.1444151698087, (29, 2784): 690.3432851076092, (29, 2800): 692.7860739971131, (29, 2802): 696.2180785650522, (29, 2803): 695.7982286819299, (29, 2804): 695.1683562852368, (29, 2805): 697.2126418283468, (29, 2807): 697.0760220961691, (29, 2809): 696.9228741604684, (29, 2812): 690.9672501466232, (29, 2814): 697.1595205785766, (29, 2817): 698.0963190088677, (29, 2819): 696.9960582780436, (29, 2823): 692.2288368201908, (29, 2832): 698.4406281483489, (29, 2836): 694.3922794662386, (29, 2839): 696.9814242323779, (29, 2841): 697.9196310422632, (29, 2843): 697.487146706508, (29, 2846): 695.5189728586934, (29, 2849): 699.2088725277093, (29, 2852): 698.2377102498214, (29, 2853): 699.6608968402443, (29, 2876): 700.4497335766368, (29, 2877): 703.7530529140907, (29, 2885): 705.5175646424166, (29, 2918): 696.9437166274175, (29, 2921): 698.4373308636768, (29, 2925): 691.1713437262646, (29, 2926): 688.6004174481972, (29, 2930): 694.817563165488, (29, 2931): 691.9948299238929, (29, 2938): 697.100604390132, (29, 2940): 700.512593000895, (29, 2947): 695.5591664824442, (29, 2949): 694.4603608077956, (29, 2950): 695.2267582528779, (29, 2952): 694.5396628700987, (29, 2958): 694.3483621314482, (29, 2959): 694.8559286751613, (29, 2960): 696.448561763075, (29, 2961): 695.7721629439471, (29, 2963): 693.8424893187641, (29, 2968): 694.3642213960354, (29, 2976): 693.5751364428046, (29, 2981): 681.4501606735871, (29, 2982): 681.2418313191943, (29, 2984): 680.5996736772079, (29, 3003): 679.5915541009952, (29, 3046): 668.7582768568839, (29, 3050): 676.6662942046156, (29, 3051): 677.1415157394566, (29, 3053): 675.708340040251, (29, 3069): 684.3887776438046, (29, 3071): 674.9641886352524, (29, 3080): 705.8248413817934, (29, 3199): 678.4298730136076, (29, 3200): 676.9682960736463, (29, 3205): 686.6111546246129, (29, 3209): 677.8143352778596, (29, 3215): 676.9677595502551, (29, 3217): 675.0487710986988, (29, 3249): 677.0391063564116, (29, 3263): 691.4882533865483, (29, 3289): 681.3403153396731, (29, 3301): 682.0555557456753, (29, 3302): 681.2701112774118, (29, 3307): 680.3813207298584, (29, 3310): 682.8820361738924, (29, 3391): 689.7570717304695, (29, 3509): 365.8005326303139, (29, 3510): 364.41415064696025, (29, 3511): 365.1877806549691, (29, 3512): 364.19946271012304, (29, 3514): 364.3732573892597, (29, 3519): 369.7928370920842, (29, 3536): 367.98413632190704, (29, 3545): 370.0110553125488, (29, 3548): 367.69206586792865, (29, 3572): 368.9521295527381, (29, 3581): 367.7745621908642, (29, 3583): 366.2118358655696, (29, 3601): 372.6328353072917, (29, 3656): 370.98153960681174, (29, 3669): 369.60820763418434, (29, 3670): 370.90630962650965, (29, 3695): 363.2515269348828, (29, 3696): 364.2081528358819, (29, 3782): 365.7701116201678, (29, 3792): 364.5978677251938, (29, 3989): 254.13512795549062, (29, 4008): 261.9173763428575, (29, 4031): 262.62772658378316, (29, 4045): 258.70699333442536, (29, 4144): 258.02838842532555, (29, 4145): 249.0665185639868, (29, 4164): 254.74714564067324, (29, 4168): 251.7812753209652, (29, 4173): 251.02105078603145, (29, 4181): 246.28230022584287, (29, 4228): 243.0199921088628, (29, 4248): 239.44055420520354, (29, 4254): 192.5600291644822, (29, 4260): 193.11721671682233, (29, 4262): 195.59789682529893, (29, 4273): 195.2607910550942, (29, 4319): 167.39370504299944, (29, 4326): 166.6052546199339, (29, 4328): 167.03285156283704, (29, 4334): 168.4085673320434, (29, 4335): 167.72784722765172, (29, 4372): 210.36020390122383, (29, 4413): 235.42313009124302, (29, 4434): 208.4897836144485, (29, 4447): 208.44514733086626, (29, 4452): 209.2552152263464, (29, 4463): 189.25938649207413, (29, 4465): 189.10215630558048, (29, 4619): 246.9516714027885, (29, 4645): 249.38909753973945, (29, 4657): 249.9088435642373, (29, 4666): 249.43485355638907, (29, 4676): 252.08587595689818, (29, 4678): 252.14698122028048, (29, 4689): 251.6795896117272, (29, 4704): 265.2625501617265, (29, 4726): 321.035730447638, (29, 4727): 320.10697627129053, (29, 4730): 318.2375330317116, (29, 4731): 319.2226120198771, (29, 4734): 317.6868645998855, (29, 4735): 317.1887377515755, (29, 4736): 317.96504374808694, (29, 4737): 316.8564674428964, (29, 4738): 317.33461073569896, (29, 4756): 318.46832952077585, (29, 4760): 311.93425009826575, (29, 4761): 311.7132731122733, (29, 4762): 311.1188080711378, (29, 4765): 312.6155341995613, (29, 4773): 322.49086067472723, (29, 4774): 322.2657817739035, (29, 4790): 321.7838889404654, (29, 4795): 320.8224167722322, (29, 4799): 322.9869694381453, (29, 4801): 325.7581180950563, (29, 4804): 320.38694025346587, (29, 4805): 319.60617139628243, (29, 4806): 322.80590750206864, (29, 4815): 322.45154070712624, (29, 4816): 324.49828059219897, (29, 4817): 325.6571739307394, (29, 4826): 324.0587142633474, (29, 4830): 323.04085717164867, (29, 4839): 314.67318049426984, (29, 4840): 315.79810259680715, (29, 4841): 314.08423755873633, (29, 4846): 313.3237759243538, (29, 4848): 313.71291410791395, (29, 4850): 314.6583004071013, (29, 4871): 301.1549448844278, (29, 4883): 310.020284596135, (29, 4900): 304.6269080832063, (29, 4901): 303.94578774450224, (29, 4917): 259.530898039043, (29, 4931): 253.70336902859285, (29, 4944): 259.6925933308452, (29, 4956): 255.2755990981716, (29, 4958): 256.110715873991, (29, 4959): 255.70114917666413, (29, 4961): 256.0459354734129, (29, 4966): 254.43768407081154, (29, 5207): 248.13068886174662, (29, 5272): 102.07249952052751, (29, 5283): 104.56995913718076, (29, 5287): 111.37928604058136, (29, 5289): 112.57367118551048, (29, 5293): 99.7759088280339, (29, 5295): 106.43299990970824, (29, 5296): 108.04980747170504, (29, 5298): 108.91101996185627, (29, 5303): 112.30979169669094, (29, 5305): 104.15395081075981, (29, 5306): 104.93870736370674, (29, 5307): 103.10090584316622, (29, 5308): 105.81064054038124, (29, 5313): 103.45920193370443, (29, 5314): 104.27538775785686, (29, 5317): 107.00519034269931, (29, 5319): 110.46022990097244, (29, 5324): 107.81964444700779, (29, 5326): 106.02259624974128, (29, 5348): 106.00580564905499, (29, 5351): 110.31938231896879, (29, 5399): 116.44887393129015, (29, 5413): 117.38142652985042, (29, 5422): 115.96409590926396, (29, 5445): 111.45996202477926, (29, 5448): 109.29953299746212, (29, 5456): 110.71129976409671, (29, 5467): 113.21330173206078, (29, 5624): 83.44965796129533, (29, 5671): 136.78908197540827, (29, 5672): 133.44304588293895, (29, 5797): 175.59261442139476, (29, 5871): 163.09140048629493, (29, 5976): 139.38394428844384, (29, 6118): 545.1323767673498, (29, 6248): 579.3757926951013, (29, 6345): 105.85384286099107, (29, 6352): 111.32019419132813, (29, 6354): 103.86720828405333, (29, 6359): 104.02313633209106, (29, 6376): 113.330509356812, (29, 6378): 104.64065557145089, (29, 6381): 105.29917612300464, (29, 6383): 106.5223098835557, (29, 6396): 110.71664698857623, (29, 6399): 107.23560948196307, (29, 6408): 109.94688599361965, (29, 6409): 104.2343522230298, (29, 6419): 108.75601934243755, (29, 6422): 106.78483763571992, (29, 6423): 107.06543112449434, (29, 6424): 100.8345676793597, (29, 6439): 100.86911845540222, (29, 6464): 101.42490806989566, (29, 6465): 103.04459145018771, (29, 6469): 104.62045818639885, (29, 6470): 105.48065328146659, (29, 6472): 102.720653098053, (29, 6480): 98.47182857345467, (29, 6486): 89.64726820905817, (29, 6497): 92.33783918282695, (29, 6503): 94.84187397795473, (29, 6508): 97.79861850143898, (29, 6509): 95.18055874942698, (29, 6521): 95.41860438547442, (29, 6544): 92.47149302424367, (29, 6552): 100.34744723373109, (29, 6553): 100.89534077756356, (29, 6554): 101.50211642935142, (29, 6578): 99.9171414792458, (29, 6582): 97.0444397012799, (29, 6601): 98.95283713004535, (29, 6609): 97.80457732531855, (29, 6610): 96.89512756053604, (29, 6611): 98.71580228972563, (29, 6614): 100.17000045700824, (29, 6615): 99.38943099333028, (29, 6616): 96.27137941843053, (29, 6617): 97.42258516204124, (29, 6618): 94.01459353486685, (29, 6619): 100.20114858207221, (29, 6620): 95.05470122797244, (29, 6621): 95.31278325800115, (29, 6622): 96.02550778693545, (29, 6623): 98.91199192983473, (29, 6624): 98.10532736204978, (29, 6625): 98.8445244486194, (29, 6626): 100.75254728907656, (29, 6627): 101.34233185914361, (29, 6628): 93.93481404475516, (29, 6629): 96.49765626645876, (29, 6630): 101.19285743059052, (29, 6632): 97.21288357243715, (29, 6634): 100.97850193805725, (29, 6635): 96.14232412936391, (29, 6636): 95.82608028155536, (29, 6637): 97.07281263319643, (29, 6638): 99.99537214827748, (29, 6639): 100.5895066216635, (29, 6640): 100.51387696268185, (29, 6641): 94.38822799853178, (29, 6642): 99.18974384829026, (29, 6643): 101.66304245760276, (29, 6645): 99.58643487989939, (29, 6646): 95.14428086483868, (29, 6647): 99.47754269577725, (29, 6653): 99.78235462361093, (29, 6655): 100.97465181831417, (29, 6658): 100.55257073847069, (29, 6662): 98.36776935259128, (29, 6819): 121.69337313332974, (29, 6996): 94.64473247841256, (29, 7059): 84.97737695270895, (29, 7187): 85.56683629396564, (29, 7304): 116.39493777313638, (29, 7528): 85.60749530180837, (29, 7720): 46.735051499753816, (29, 7793): 39.87426346201171, (29, 7807): 41.93143899064051, (29, 7808): 38.325438493187356, (29, 7831): 85.92386363727037, (29, 7850): 87.05763548027602, (29, 7852): 89.87383581406, (29, 8012): 58.00241954909052, (29, 8125): 24.0, (29, 8208): 44.05916701250308, (29, 8392): 62.32340047809859, (29, 8651): 169.66673008775805, (29, 9088): 142.415350830533, (29, 9443): 176.32187589581605, (29, 9444): 174.58367788855512, (29, 9828): 226.47787509057576, (29, 9868): 228.51579344664327, (29, 10180): 24.0, (29, 10256): 28.456280527246527, (29, 10276): 24.0, (29, 10378): 28.72547469153103, (29, 10676): 31.218614296254373, (29, 10714): 46.555300259182026, (29, 10730): 30.174711560811012, (29, 10862): 219.0741816925989, (29, 10881): 219.91950225038406, (29, 10883): 220.52354918358245, (29, 10885): 218.72653547164333, (29, 10891): 221.485370161411, (29, 10909): 219.7379886714973, (29, 10911): 218.14085310616156, (29, 10913): 218.49722775284727, (29, 10915): 217.60209739906747, (29, 10919): 216.97703113367677, (29, 11037): 234.27724245574177, (29, 11039): 226.19822349391663, (29, 11516): 349.1187381656181, (29, 11856): 169.1055163009035, (29, 11857): 167.4112661913103, (29, 11861): 168.27932009241408, (29, 11881): 167.8918204538982, (29, 11902): 162.91749188404364, (29, 11911): 162.73499689804189, (29, 11914): 163.10518039082882, (29, 11922): 166.55131124288076, (29, 11924): 167.9006807008275, (29, 11926): 166.51108559683, (29, 11950): 170.12122201720703, (29, 11963): 174.6704837718659, (29, 11983): 172.8617744794453, (29, 11985): 176.89512358917224, (29, 12009): 177.078016589399, (29, 12010): 173.58224518538057, (29, 12018): 174.2663201247229, (29, 12020): 174.97794362737503, (29, 12021): 175.63574379386634, (29, 12024): 178.72233812251696, (29, 12025): 177.45342429706437, (29, 12027): 176.7769409624107, (29, 12031): 173.03636708909843, (29, 12032): 173.9316107805445, (29, 12035): 177.13560196632392, (29, 12041): 176.70010870007, (29, 12045): 135.27733709313415, (29, 12145): 156.06681697502086, (29, 12275): 260.1549417671186, (29, 12294): 254.4929252168628, (29, 12358): 280.5483957495371, (29, 12463): 292.0370830463608, (29, 12465): 291.88186976064316, (29, 12482): 294.1707174042108, (29, 12503): 294.047146345446, (29, 12506): 295.1210304795629, (29, 12549): 290.6847832706337, (29, 12559): 290.27962039967895, (29, 12569): 291.90952587235694, (29, 12572): 292.6751796390502, (29, 12574): 290.8420338100143, (29, 12576): 291.37307739663066, (29, 12591): 290.0009569654311, (29, 12608): 295.7479315763142, (29, 12696): 284.43587568702327, (29, 12710): 289.13407927826006, (29, 12728): 287.7019968926815, (29, 12766): 132.6538832691775, (29, 12771): 118.3079354299092, (29, 12790): 118.02973293802448, (29, 12795): 118.66961076321064, (29, 12797): 106.85002674552787, (29, 12798): 107.21057058855816, (29, 12811): 112.58090621400348, (29, 12830): 112.59237771239007, (29, 12848): 109.7660142070032, (29, 12850): 107.9844579585209, (29, 12852): 111.2025199631339, (29, 12854): 110.41556364109606, (29, 12859): 109.61302980843297, (29, 12861): 107.18058709972769, (29, 12865): 115.25142867495038, (29, 12866): 113.72121126696905, (29, 12867): 116.40252316597679, (29, 12874): 115.2508837921706, (29, 12875): 115.42734112525915, (29, 12881): 114.10039642230119, (29, 12883): 114.98472152930371, (29, 12885): 116.24034977112377, (29, 12888): 113.78457167699575, (29, 12889): 112.83362572518303, (29, 12892): 115.85313171639153, (29, 12893): 114.58082534501285, (29, 12896): 114.30178673441175, (29, 12906): 118.65731354972193, (29, 13018): 132.8304144137706, (29, 13071): 137.53724532624676, (29, 13131): 114.76602978014223, (29, 13146): 114.32374084650283, (29, 13159): 134.45831766881955, (29, 13193): 112.78889158105206, (29, 13198): 100.8090059517135, (29, 13292): 103.27945561746805, (29, 13296): 96.94006124992764, (29, 13406): 113.57995704688905, (29, 13407): 114.65729432398217, (29, 13417): 123.286410619998, (29, 13418): 124.73555342301529, (29, 13438): 118.37859123902673, (29, 13442): 115.62706533457069, (29, 13443): 115.86995154509349, (29, 13764): 215.13476920985542, (29, 13766): 213.92885438664675, (29, 13771): 217.70286124764874, (29, 13783): 211.84994972929402, (29, 13784): 211.4955961488159, (29, 13792): 223.9248798227446, (29, 13824): 213.21105535806456, (29, 14017): 191.01884810633587, (29, 14870): 183.14975986070826, (29, 14997): 93.711785478432, (29, 15000): 93.22268241790735, (29, 15003): 91.7041229479205, (29, 15006): 90.38692105521923, (29, 15007): 89.09389091656631, (29, 15056): 88.1974736116804, (29, 15063): 89.14559114330042, (29, 15069): 89.26173669139935, (29, 15076): 88.61933938884843, (29, 15086): 93.05706735611233, (29, 15087): 93.86194083809292, (29, 15111): 98.00326997636024, (29, 15116): 95.58446456017718, (29, 15722): 129.0686799737962, (29, 15998): 149.2671567679858, (29, 16073): 453.7581928640407, (29, 16939): 572.1756238490054, (29, 16940): 570.3179005428223, (29, 16951): 572.7394029309748, (29, 16963): 572.8418834448506, (29, 16965): 574.9679731815729, (29, 16969): 574.6125312888659, (29, 16970): 573.5518529555902, (29, 16971): 571.6249139582682, (29, 16973): 571.60693425228, (29, 16974): 575.9288198272732, (29, 16976): 573.6312932709649, (29, 16978): 572.1845708923884, (29, 16980): 574.2499632790744, (29, 16982): 576.0298899301574, (29, 17045): 645.749234738687, (29, 17048): 648.301178168679, (29, 17304): 226.90197819065213, (29, 17305): 226.46971952089874, (29, 17330): 227.39588050061684, (29, 17334): 224.32799154738578, (29, 17343): 229.38042387837717, (29, 17345): 225.09139176949697, (29, 17347): 227.79268573472515, (29, 17351): 221.02690734627828, (29, 17372): 224.37597077971876, (29, 17373): 229.10707449073274, (29, 17377): 229.50936619664685, (29, 17382): 226.60920005367964, (29, 17383): 226.8620319325237, (29, 17389): 225.21885151656886, (29, 17400): 228.0326930613637, (29, 17401): 227.84116468875166, (29, 17402): 228.28592189000966, (29, 17403): 228.64396174034638, (29, 17440): 226.2255291372045, (29, 17455): 229.44583228948838, (29, 17491): 230.37898122833002, (29, 17507): 220.7365247562439, (29, 17509): 222.13185550344107, (29, 17590): 220.92963694093854, (29, 17615): 207.11939008821747, (29, 17642): 209.0558471148194, (29, 17643): 209.183535467949, (29, 17668): 206.8949161426502, (29, 17721): 201.79676970928458, (29, 17754): 216.50150659363536, (29, 17769): 220.41843582014027, (29, 17776): 215.4876162551695, (29, 17804): 222.8695710849837, (29, 17809): 224.46024841905162, (29, 17824): 222.9817675354557, (29, 17837): 220.57001101933193, (29, 17838): 221.19509559268505, (29, 17862): 220.23938702969485, (29, 17866): 223.38646379448417, (29, 17872): 218.82447019790615, (29, 17873): 216.52741600762354, (29, 17881): 220.12282254457722, (29, 17947): 418.0402239025149, (29, 17951): 414.78274773566756, (29, 17953): 414.0452076413102, (29, 17954): 414.1980600693264, (29, 17959): 417.5684017314071, (29, 17963): 416.624715430814, (29, 18000): 399.76607353351494, (29, 18001): 400.2529465648556, (29, 18111): 443.60969236854527, (29, 18148): 357.1216506917007, (29, 18166): 390.2005475288619, (29, 18189): 421.8180822640455, (29, 18239): 229.5907283176529, (29, 18240): 229.6575192482498, (29, 18245): 229.78309225226712, (29, 18247): 229.52792981239682, (29, 18251): 229.88163043275742, (29, 18256): 230.3655793002908, (29, 18258): 230.018223094883, (29, 18259): 230.13660847641296, (29, 18260): 230.3565047051937, (29, 18262): 230.71054343645014, (29, 18263): 230.51915865566755, (29, 18264): 230.73210529680887, (29, 18266): 230.90630505943483, (29, 18267): 231.10294136806306, (29, 18268): 231.23255086357773, (29, 18269): 231.63432921581628, (29, 18275): 231.4451223390555, (29, 18285): 230.62544431333222, (29, 18308): 226.44530552695207, (29, 18313): 225.26902042297868, (29, 18314): 226.06469599209655, (29, 18315): 231.3705268469814, (29, 18316): 231.4576015455705, (29, 18317): 231.65281472085772, (29, 18320): 231.66616396506495, (29, 18321): 231.8264297581642, (29, 18322): 232.1100828543319, (29, 18324): 232.17330014469218, (29, 18325): 232.89178652626012, (29, 18326): 232.61870438442858, (29, 18327): 231.9307768162347, (29, 18329): 233.0839065610492, (29, 18330): 233.09049733494342, (29, 18331): 232.55136021062648, (29, 18332): 232.05721226865973, (29, 18333): 232.91035510709264, (29, 18336): 232.33135035107645, (29, 18337): 232.50086075655028, (29, 18403): 232.80269452676743, (29, 18432): 226.77095584631414, (29, 18451): 230.82362952703514, (29, 18466): 234.67195635523123, (29, 18481): 231.24867944673156, (29, 18483): 231.3307409724473, (29, 18484): 230.87220858803096, (29, 18485): 229.4097609407966, (29, 18486): 230.1797521254904, (29, 18487): 229.16217347920988, (29, 18489): 230.34555193663286, (29, 18490): 231.04190539780302, (29, 18491): 231.47456115960188, (29, 18492): 228.3053872508906, (29, 18493): 229.92923865474648, (29, 18494): 230.2361837608412, (29, 18495): 230.70730462246198, (29, 18496): 230.32063687250377, (29, 18497): 228.85321154681344, (29, 18498): 229.39490859619704, (29, 18499): 230.09969339337658, (29, 18501): 229.44534909713104, (29, 18502): 228.98521490349268, (29, 18503): 228.73136562970708, (29, 18504): 230.60068027457976, (29, 18506): 229.2796563927019, (29, 18507): 228.7953776110743, (29, 18508): 229.92210833848853, (29, 18509): 229.8536806013251, (29, 18510): 228.62899733279315, (29, 18511): 229.89999726623867, (29, 18512): 229.52229268852392, (29, 18515): 230.52689594709966, (29, 18516): 230.29468014856144, (29, 18517): 229.59842195026076, (29, 18518): 230.73704125946261, (29, 18519): 230.74537500825596, (29, 18520): 229.88702991541257, (29, 18522): 232.81182020114588, (29, 18523): 232.81648858171536, (29, 18532): 233.301933651071, (29, 18535): 232.20032253690673, (29, 18537): 231.58732871210543, (29, 18539): 231.6677369529253, (29, 18540): 231.68873175778577, (29, 18541): 231.9491698284705, (29, 18542): 232.12330600601535, (29, 18543): 231.22164535263605, (29, 18546): 231.49555927435676, (29, 18555): 232.44996714273702, (29, 18556): 232.5624697231646, (29, 18565): 233.10838420680867, (29, 18567): 233.2103199639647, (29, 18568): 232.76514191354784, (29, 18577): 236.54372564930208, (29, 18583): 236.15507113543785, (29, 18605): 237.24744724724613, (29, 18608): 233.1784591693324, (29, 18616): 240.755759326182, (29, 18618): 243.59512436797746, (29, 18625): 243.22064892673978, (29, 18645): 240.85462729451172, (29, 18646): 241.3209041822322, (29, 18653): 238.18764098158883, (29, 18654): 240.5726627249251, (29, 18655): 238.86990033301333, (29, 18666): 249.71083001588676, (29, 18837): 251.12043422137924, (29, 18974): 233.21797002290518, (29, 18999): 237.05678250143805, (29, 19000): 237.96934428435526, (29, 19174): 205.81393407632814, (29, 19342): 226.37510703715247, (29, 19455): 204.41939906879205, (29, 19555): 169.8311884127513, (29, 19564): 178.43101705303528, (29, 19573): 175.425121461683, (29, 19586): 173.66699381642644, (29, 19605): 173.26381827812324, (29, 19611): 175.052352135836, (29, 19614): 172.52136644408424, (29, 19641): 195.05924298299936, (29, 19702): 196.5079242144823, (29, 19713): 194.46571312968888, (29, 19731): 154.30905428887647, (29, 19819): 200.9985110466047, (29, 19893): 116.99300035331686, (29, 19899): 129.76787086196157, (29, 19929): 119.88227145938174, (29, 19951): 143.5544435145663, (29, 19962): 122.6802516546939, (29, 19970): 126.207198904152, (29, 19971): 126.65662581630365, (29, 19972): 124.93956519955358, (29, 19975): 123.75450327421343, (29, 19978): 146.8591063230554, (29, 19987): 147.05521125749968, (29, 19989): 140.62754838785216, (29, 20039): 148.14206959617604, (29, 20043): 150.56365727434135, (29, 20047): 148.30006268102258, (29, 20052): 141.41067001977285, (29, 20054): 142.078522434323, (29, 20085): 172.6713506220743, (29, 20104): 174.62236834083302, (29, 20132): 162.86584846284313, (29, 20203): 120.42531852709402, (29, 20280): 119.76663660894351, (29, 20285): 120.00974555682919, (29, 20290): 120.49567290751753, (29, 20297): 118.12182270119676, (29, 20309): 151.37430537773662, (29, 20453): 182.11275537140145, (29, 20485): 103.42596539906805, (29, 20520): 97.35625134069795, (29, 20526): 97.40804825658735, (29, 20698): 291.7713663266295, (29, 20868): 343.827488383099, (29, 21042): 67.00856504645468, (29, 21057): 78.42941471784738, (29, 21066): 70.93093621484022, (29, 21075): 71.45096879573137, (29, 21093): 65.20810874505806, (29, 21098): 70.05740099422576, (29, 21127): 66.50668737069242, (29, 21130): 67.38635387847008, (29, 21144): 69.49774075301384, (29, 21146): 65.78929897198056, (29, 21147): 70.05918769017202, (29, 21148): 71.1322003642667, (29, 21153): 77.01169095094015, (29, 21293): 83.18029619784689, (29, 21426): 103.67418200426152, (29, 21442): 119.41510973166109, (29, 21451): 120.82772794981477, (29, 21466): 110.13864665109209, (29, 21469): 111.25813293424625, (29, 21471): 109.63629294342606, (29, 21473): 110.24354560931688, (29, 21475): 109.35949308297812, (29, 21482): 112.97686432392052, (29, 21484): 112.21266061140815, (29, 21488): 111.824788062025, (29, 21494): 107.94017481215604, (29, 21498): 109.13605515870948, (29, 21500): 106.13598785086404, (29, 21514): 104.0788554722585, (29, 21537): 102.7299766148027, (29, 21662): 102.10713838021012, (29, 21691): 95.97735050239021, (29, 21757): 97.23127053444334, (29, 21777): 38.27070474772788, (29, 21778): 37.12090794757496, (29, 21779): 36.25783531531898, (29, 21790): 41.226688366228245, (29, 21802): 38.32874883194805, (29, 21824): 38.356078634136566, (29, 21874): 34.78159385094744, (29, 21879): 31.402624402294897, (29, 21983): 51.34823695287673, (29, 22002): 59.27959757094501, (29, 22132): 80.7301578161923, (29, 22261): 244.03381849632208, (29, 22298): 240.14688260871145, (29, 22339): 265.2333479678802, (29, 22508): 203.59508670799715, (29, 22841): 693.6568202039849, (29, 22842): 693.5927186365428, (29, 22874): 688.4219632452074, (29, 22941): 689.1779004365666, (29, 22956): 692.1171765009159, (29, 22960): 693.1806451784736, (29, 22968): 695.1204860173688, (29, 22970): 696.093007727593, (29, 22974): 696.9216030623041, (29, 22980): 700.5220433641434, (29, 23025): 699.2058071954875, (29, 23028): 698.2028113866255, (29, 23081): 703.0643847115881, (29, 23104): 694.905532522373, (29, 23147): 665.8430163217714, (29, 23298): 127.52574094168017, (29, 23376): 121.98120749771743, (29, 23381): 114.48349506225068, (29, 23529): 127.81625293760433, (29, 23556): 125.04951139201809, (29, 23718): 127.79423810003465, (29, 24001): 161.62789902790325, (29, 24094): 166.53895434679396, (29, 24129): 172.28406644725604, (29, 24174): 158.37719880477843, (29, 24235): 170.01247859925525, (29, 24259): 176.69472779721778, (29, 24260): 176.10143614778357, (29, 24261): 175.03331292386105, (29, 24305): 183.7735945284198, (29, 24306): 184.64931348029646, (29, 24307): 183.10759307896907, (29, 24308): 179.75738839966277, (29, 24498): 202.01304205194052, (29, 24499): 202.04489841312287, (29, 24500): 201.08863467581256, (29, 24668): 199.3849002048352, (29, 24711): 207.15012193369753, (29, 24756): 209.5498297885051, (29, 24788): 211.78267463484062, (29, 24809): 204.02623608364868, (29, 24813): 206.55130964552447, (29, 24821): 205.77045668454176, (29, 24825): 206.13379372905666, (29, 24832): 203.67190320069102, (29, 24833): 204.72914294965815, (29, 24835): 205.71794627402434, (29, 24837): 207.55151505816164, (29, 24840): 203.43126608187558, (29, 24841): 205.22483493056848, (29, 24844): 203.3758652524438, (29, 24845): 204.74762279071234, (29, 24846): 204.08356011649215, (29, 24849): 204.61040078827665, (29, 24850): 206.74485054052258, (29, 24863): 192.8014885899348, (29, 24866): 194.733704982653, (29, 24885): 196.61806526105644, (29, 24886): 196.55282671889492, (29, 24889): 201.54193876553836, (29, 24903): 203.53160373347012, (29, 24909): 197.21224241175247, (29, 24999): 282.4533632674178, (29, 25019): 281.32059074198935, (29, 25028): 281.09589362420735, (29, 25137): 135.0113757114025, (29, 25145): 136.71934304049074, (29, 25208): 167.96618928227088, (29, 25233): 166.0027382719158, (29, 25371): 128.06168409338008, (29, 25377): 120.77081796631556, (29, 25828): 54.652330954634536, (29, 25851): 50.96115545137464, (29, 25874): 48.05297906575321, (29, 25898): 56.96170447422798, (29, 25946): 54.35007854291254, (29, 26047): 76.972527367832, (29, 26066): 72.54210999491741, (29, 26197): 63.718600386193415, (29, 26212): 108.33999723166404, (29, 26253): 114.38515039348931, (29, 26254): 111.51165239915989, (29, 26257): 111.22116904293313, (29, 26258): 113.68941545397115, (29, 26260): 112.2795364874015, (29, 26266): 110.52190533922699, (29, 26267): 109.4424939129381, (29, 26271): 109.88548766262119, (29, 26304): 86.95799488968568, (29, 26305): 85.74368993227128, (29, 26363): 67.3326845687816, (29, 26441): 255.86528503391494, (29, 26442): 255.19092945817812, (29, 26450): 251.93980547290585, (29, 26459): 251.73243575209256, (29, 26462): 252.2163465600997, (29, 26467): 261.74975344073425, (29, 26471): 259.04650559695045, (29, 26472): 258.7556946697665, (29, 26473): 258.6391740489503, (29, 26476): 257.07667080030484, (29, 26485): 253.32460620705876, (29, 26493): 253.40452671406842, (29, 26524): 253.68168318103397, (29, 26525): 253.2854296103634, (29, 26556): 257.7593049684533, (29, 26560): 257.5004906144085, (29, 26561): 255.4569834926512, (29, 26564): 256.8673228008566, (29, 26569): 254.93282645917455, (29, 26570): 254.08935486012624, (29, 26573): 254.588631029619, (29, 26581): 254.4992780899334, (29, 26583): 253.79533969600178, (29, 26593): 254.51118350127086, (29, 26837): 262.37933379853513, (29, 26844): 264.5649258946776, (29, 26863): 259.7912260304329, (29, 26893): 266.06835053000447, (29, 26902): 269.03069953781744, (29, 26905): 266.04344444532455, (29, 26912): 268.35164872292506, (29, 26921): 262.79815848447845, (29, 26922): 256.89957997300513, (29, 27212): 282.61437466216665, (29, 27218): 280.3943976705683, (29, 27239): 286.7310268652124, (29, 27257): 284.4019996506545, (29, 27274): 287.5040806251643, (29, 27279): 286.8793065467104, (29, 27282): 284.4127762723981, (29, 27283): 285.6923922732874, (29, 27285): 288.5274518817387, (29, 27286): 285.9984410012504, (29, 27290): 282.2788623752519, (29, 27295): 280.99556713947237, (29, 27300): 287.9913920443425, (29, 27344): 280.6923162616671, (29, 27366): 283.3428515114853, (29, 27383): 288.4224228381105, (29, 27398): 291.80471946239516, (29, 27406): 289.46569371613805, (29, 27407): 290.32027414442524, (29, 27426): 288.2186079688412, (29, 27432): 277.21510586912643, (29, 27460): 284.26912774875365, (29, 27523): 282.1710778991769, (29, 27545): 328.2568270563078, (29, 27602): 383.56996352286023, (29, 27606): 384.7205247316727, (29, 27646): 324.23656508435886, (29, 27667): 335.4392680994384, (29, 27672): 336.0878827104084, (29, 27674): 334.1401367588185, (29, 27688): 335.9888324739091, (29, 27692): 337.95602317816133, (29, 27693): 336.2661911629077, (29, 27705): 336.1104705840161, (29, 27712): 336.8855083181444, (29, 27786): 389.49876649939847, (29, 27790): 384.6418029177186, (29, 27791): 384.33228233812355, (29, 27795): 386.2551851215495, (29, 27801): 382.48586647093015, (29, 27813): 391.0656889727165, (29, 27816): 389.29720300897725, (29, 27823): 382.35764985684824, (29, 27830): 387.1498307570815, (29, 27884): 304.8489618967698, (29, 27885): 319.42128324968957, (29, 27896): 310.64123578798615, (29, 27919): 310.10160321146424, (29, 27922): 311.8202954831165, (29, 27930): 307.14023630332645, (29, 27934): 307.64250811936006, (29, 27935): 307.9917658172536, (29, 27948): 375.167598883541, (29, 27951): 378.909444282871, (29, 28061): 325.30399768769087, (29, 28290): 441.2113859014474, (29, 28292): 443.6785682593498, (29, 28293): 441.6953305186967, (29, 28295): 440.72041949618813, (29, 28296): 441.1072240186933, (29, 28297): 439.9083562832274, (29, 28302): 439.0828951859813, (29, 28310): 496.57523272303536, (29, 28313): 499.06296223952927, (29, 28372): 498.1345906529239, (29, 28398): 498.41669663192465, (29, 28399): 497.7226675603229, (29, 28400): 499.01031360677615, (29, 28401): 495.4748085024266, (29, 28445): 498.3009152012134, (29, 28475): 492.0287435958136, (29, 28885): 163.10902787941663, (29, 28886): 161.75892575289214, (29, 28915): 161.7213992938616, (29, 28916): 161.10080554200326, (29, 28917): 160.2972617624524, (29, 28921): 165.3718904566207, (29, 28931): 164.8004867639795, (29, 28945): 156.2836699408644, (29, 28982): 158.54697975907922, (29, 29219): 161.18323285487966, (29, 29228): 156.38521807119616, (29, 29246): 186.843707359989, (29, 29248): 186.2580794325819, (29, 29282): 179.7488059626031, (29, 29290): 190.25743103149495, (29, 29291): 188.88754514332493, (29, 29292): 190.13589180419106, (29, 29293): 187.60247398936417, (29, 29294): 189.5235922090524, (29, 29298): 187.7317546530554, (29, 29299): 187.45623715827082, (29, 29304): 185.22780771150948, (29, 29317): 179.26983709651185, (29, 29323): 178.81885961751004, (29, 29330): 181.66761052924176, (29, 29331): 183.15172204641368, (29, 29344): 160.95696240610306, (29, 29445): 104.54620690380833, (29, 29724): 687.2549800841986, (29, 29738): 688.2103342553172, (29, 29745): 685.4926507145287, (29, 29748): 686.3988321377911, (29, 29750): 688.1116629873669, (29, 29759): 685.0449971738167, (29, 29772): 688.5818516822527, (29, 29781): 687.8199538994487, (29, 29784): 687.061286763946, (29, 29790): 688.6530966222401, (29, 29811): 686.7997638413776, (29, 29817): 694.2974979234906, (29, 29818): 693.5630387148758, (29, 29929): 684.9395160013174, (29, 30039): 696.4396886921019, (29, 30066): 687.8480896995632, (29, 30116): 656.0507398800604, (29, 30238): 608.9665004759792, (29, 30248): 631.0707699785575, (29, 30260): 631.5080007310977, (29, 30545): 150.68421473826007, (29, 30733): 105.98818054759583, (29, 30756): 83.92139004514503, (29, 30921): 110.47565939850007, (29, 31079): 141.87938486047804, (29, 31149): 126.09954898889384, (29, 31154): 128.73043427422652, (29, 31160): 125.75814042176002, (29, 31163): 128.71653971611107, (29, 31189): 125.03026259334061, (29, 31215): 127.4357070457138, (29, 31259): 139.02378889597347, (29, 31262): 138.2035155701139, (29, 31430): 150.13379766216278, (29, 31568): 171.6252629182603, (29, 31751): 146.6031665789781, (31, 109): 638.394675226212, (31, 872): 127.64126757749199, (31, 873): 125.16422415354, (31, 877): 125.4499871523345, (31, 879): 125.01962831006009, (31, 884): 126.1287716070947, (31, 889): 124.85569161512154, (31, 891): 127.11779409755886, (31, 892): 123.2287926397439, (31, 894): 123.80634081200853, (31, 896): 127.27657181496744, (31, 903): 124.63540082391285, (31, 909): 130.9542902780978, (31, 910): 130.57510190276395, (31, 912): 132.0628383972281, (31, 913): 133.48440176035157, (31, 916): 134.96962001725774, (31, 926): 130.5852594513406, (31, 927): 131.55054101379184, (31, 948): 128.12040445157226, (31, 961): 129.2272618010306, (31, 962): 129.37346293530058, (31, 963): 129.40432589256704, (31, 967): 123.83919263557421, (31, 974): 123.73500868772929, (31, 998): 122.337872296024, (31, 1014): 79.85624904562907, (31, 1086): 154.1300290653131, (31, 1087): 157.3241369956433, (31, 1089): 157.85916876767, (31, 1090): 156.67641205663264, (31, 1092): 153.4427649566891, (31, 1097): 155.3374756064532, (31, 1107): 153.7191491164593, (31, 1387): 520.1666152834356, (31, 1554): 552.3376306898073, (31, 1827): 24.0, (31, 1828): 24.0, (31, 1829): 24.0, (31, 1830): 24.0, (31, 1831): 24.0, (31, 1832): 24.0, (31, 1833): 24.0, (31, 1836): 24.0, (31, 1841): 24.0, (31, 1843): 24.0, (31, 1844): 24.0, (31, 1845): 24.0, (31, 1847): 24.0, (31, 1848): 24.0, (31, 1849): 24.0, (31, 1850): 24.0, (31, 1851): 24.0, (31, 1852): 24.0, (31, 1854): 24.0, (31, 1856): 24.0, (31, 1857): 24.0, (31, 1858): 24.0, (31, 1861): 24.0, (31, 1866): 24.0, (31, 1867): 24.0, (31, 1868): 24.0, (31, 1870): 24.0, (31, 1871): 24.0, (31, 1875): 24.0, (31, 1880): 24.0, (31, 1882): 24.0, (31, 1883): 24.0, (31, 1889): 24.0, (31, 1893): 24.0, (31, 1894): 24.0, (31, 1899): 24.0, (31, 1900): 24.0, (31, 1902): 24.0, (31, 1905): 24.0, (31, 1907): 24.0, (31, 1910): 24.0, (31, 1917): 24.0, (31, 1920): 24.0, (31, 1935): 24.0, (31, 1937): 24.0, (31, 1946): 24.0, (31, 1949): 24.0, (31, 1950): 24.0, (31, 1951): 24.0, (31, 1952): 24.0, (31, 1953): 24.0, (31, 1954): 24.0, (31, 1958): 24.0, (31, 1960): 24.0, (31, 1968): 24.0, (31, 1969): 24.0, (31, 1974): 24.0, (31, 1975): 24.0, (31, 1979): 24.0, (31, 1980): 24.0, (31, 1981): 24.0, (31, 1985): 24.0, (31, 1994): 24.0, (31, 2011): 24.0, (31, 2019): 24.0, (31, 2020): 24.0, (31, 2029): 24.0, (31, 2030): 24.0, (31, 2032): 24.0, (31, 2033): 24.0, (31, 2034): 24.0, (31, 2036): 24.0, (31, 2037): 24.0, (31, 2038): 24.0, (31, 2042): 24.0, (31, 2050): 24.0, (31, 2051): 24.0, (31, 2053): 24.0, (31, 2054): 24.0, (31, 2066): 24.0, (31, 2067): 24.0, (31, 2071): 24.0, (31, 2072): 24.0, (31, 2073): 24.0, (31, 2074): 24.0, (31, 2080): 24.0, (31, 2082): 24.0, (31, 2083): 24.0, (31, 2089): 24.0, (31, 2090): 24.0, (31, 2092): 24.0, (31, 2098): 24.0, (31, 2099): 24.0, (31, 2101): 24.0, (31, 2102): 24.0, (31, 2103): 24.0, (31, 2104): 24.0, (31, 2106): 24.0, (31, 2112): 24.0, (31, 2113): 24.0, (31, 2114): 24.0, (31, 2117): 24.0, (31, 2123): 41.51834138210817, (31, 2124): 41.36891990812588, (31, 2134): 39.155507700422554, (31, 2138): 39.71019199749467, (31, 2141): 39.91070403229639, (31, 2148): 29.22463002186377, (31, 2150): 39.968408541337936, (31, 2151): 38.95586512730201, (31, 2152): 39.41764559556997, (31, 2153): 30.12020517189972, (31, 2154): 31.947045221926004, (31, 2155): 30.459572725894322, (31, 2156): 31.91492224488195, (31, 2157): 25.644170836439944, (31, 2160): 34.38892484292199, (31, 2161): 38.45861914757847, (31, 2162): 26.19188407567078, (31, 2163): 26.949731676458025, (31, 2164): 26.37478663492098, (31, 2168): 34.64479151569606, (31, 2172): 29.769900475814115, (31, 2174): 37.69214096625842, (31, 2178): 28.166443594596803, (31, 2179): 28.009804828024283, (31, 2183): 38.49332263519884, (31, 2185): 37.828747613753364, (31, 2186): 38.30779395719121, (31, 2190): 35.52399761366662, (31, 2192): 36.14045828654646, (31, 2193): 38.817272114433585, (31, 2194): 39.45791964814891, (31, 2195): 38.16094741652013, (31, 2197): 35.31627774549465, (31, 2205): 34.30625673454578, (31, 2207): 33.63801451613217, (31, 2208): 33.711764969199024, (31, 2212): 41.7358683981927, (31, 2214): 41.46064345100258, (31, 2225): 36.423768166298935, (31, 2231): 61.90350515434775, (31, 2278): 24.0, (31, 2284): 24.0, (31, 2285): 24.0, (31, 2291): 24.0, (31, 2292): 24.0, (31, 2307): 24.0, (31, 2313): 24.0, (31, 2317): 24.53145892324961, (31, 2319): 24.0, (31, 2321): 24.0, (31, 2323): 24.0, (31, 2326): 24.0, (31, 2327): 24.0, (31, 2329): 24.0, (31, 2330): 24.0, (31, 2332): 24.0, (31, 2344): 24.0, (31, 2346): 24.0, (31, 2361): 27.769385750458426, (31, 2368): 24.0, (31, 2374): 24.0, (31, 2375): 24.0, (31, 2377): 24.0, (31, 2378): 24.0, (31, 2379): 24.0, (31, 2380): 24.0, (31, 2383): 24.0, (31, 2385): 24.0, (31, 2395): 24.0, (31, 2397): 24.0, (31, 2398): 24.0, (31, 2399): 24.0, (31, 2400): 24.0, (31, 2402): 24.0, (31, 2403): 24.0, (31, 2404): 24.0, (31, 2405): 24.0, (31, 2407): 24.0, (31, 2408): 24.0, (31, 2409): 24.0, (31, 2411): 24.0, (31, 2412): 24.0, (31, 2413): 24.0, (31, 2414): 24.0, (31, 2422): 24.0, (31, 2424): 24.0, (31, 2426): 24.0, (31, 2433): 24.0, (31, 2436): 24.0, (31, 2437): 24.0, (31, 2440): 24.0, (31, 2445): 24.0, (31, 2447): 24.0, (31, 2454): 24.0, (31, 2455): 24.0, (31, 2460): 24.0, (31, 2461): 24.0, (31, 2471): 34.59454092314009, (31, 2492): 63.93116976307459, (31, 2511): 53.50932352681432, (31, 2523): 58.81647713814943, (31, 2525): 60.93766967602512, (31, 2535): 37.06859173720249, (31, 2537): 37.23581448085721, (31, 2538): 35.918340571834754, (31, 2539): 41.62414929655301, (31, 2540): 37.18157476188013, (31, 2542): 39.214100201096166, (31, 2559): 47.15177728503353, (31, 2575): 50.07508146672835, (31, 2599): 24.0, (31, 2600): 24.0, (31, 2607): 24.0, (31, 2627): 75.54648978708035, (31, 2647): 81.20884981540623, (31, 2674): 73.98746452103478, (31, 2681): 76.81093243638603, (31, 2683): 76.28690171246816, (31, 2686): 73.83100232421447, (31, 2689): 94.27892703890251, (31, 2690): 95.06962047206834, (31, 2713): 119.86444334433311, (31, 2714): 123.02549528342607, (31, 2715): 123.44258179536953, (31, 2739): 122.2526914413372, (31, 2740): 111.88403408273757, (31, 2741): 111.53556924961093, (31, 2749): 124.61733153900104, (31, 2750): 123.7550471196854, (31, 2752): 123.60079836154213, (31, 2755): 124.55685445440136, (31, 2758): 125.29080002566815, (31, 2759): 124.84787720995674, (31, 2769): 123.23309289205197, (31, 2771): 114.57956452099323, (31, 2779): 121.95175845057094, (31, 2784): 120.8215908839262, (31, 2800): 128.8562647148039, (31, 2802): 114.95997591908578, (31, 2803): 113.89202253002979, (31, 2804): 113.25692273826645, (31, 2805): 118.060561508109, (31, 2807): 117.1109665484273, (31, 2809): 119.02228926670053, (31, 2812): 114.14377854748095, (31, 2814): 125.02473991005954, (31, 2817): 133.43309026838878, (31, 2819): 114.90727607016031, (31, 2823): 122.47381321496795, (31, 2832): 119.88308468550154, (31, 2836): 117.91990626806958, (31, 2839): 116.16861737912315, (31, 2841): 129.30072048729528, (31, 2843): 127.67475552460776, (31, 2846): 122.04986037954284, (31, 2849): 121.75218240909044, (31, 2852): 120.70652441989313, (31, 2853): 122.29120997375406, (31, 2876): 126.78701084695349, (31, 2877): 129.0471379714243, (31, 2885): 138.2476031511845, (31, 2918): 109.27111755569769, (31, 2921): 111.10249885874713, (31, 2925): 99.58619585237372, (31, 2926): 94.05245756964298, (31, 2930): 111.2807464747485, (31, 2931): 102.43219001209451, (31, 2938): 110.87079269711208, (31, 2940): 105.70584242554138, (31, 2947): 101.02458975964602, (31, 2949): 107.6346117272733, (31, 2950): 109.53468876666274, (31, 2952): 109.22087183754095, (31, 2958): 108.5021008010996, (31, 2959): 107.03104728430901, (31, 2960): 108.45992070371344, (31, 2961): 108.78181461089261, (31, 2963): 109.11371273574542, (31, 2968): 110.27840573688955, (31, 2976): 108.06060764420066, (31, 2981): 113.88188390752187, (31, 2982): 115.69381563290386, (31, 2984): 115.9062583190823, (31, 3003): 117.66183860345363, (31, 3046): 92.51620610121053, (31, 3050): 105.30454692552178, (31, 3051): 104.74063004606735, (31, 3053): 105.06680661181721, (31, 3069): 111.26276585532568, (31, 3071): 100.47741222859506, (31, 3080): 141.39889407754995, (31, 3199): 128.89284851552657, (31, 3200): 129.80177931830528, (31, 3205): 131.48526550336604, (31, 3209): 130.23266306767755, (31, 3215): 128.74817660104895, (31, 3217): 128.56862808203078, (31, 3249): 127.63210349416205, (31, 3263): 129.46036227109403, (31, 3289): 125.14894397911037, (31, 3301): 128.0049712685822, (31, 3302): 126.8801285868268, (31, 3307): 126.46752595530191, (31, 3310): 128.1283329025481, (31, 3391): 181.5965768156876, (31, 3509): 296.78042748302124, (31, 3510): 298.1041456979793, (31, 3511): 296.9301778253806, (31, 3512): 297.50019681630624, (31, 3514): 296.99790175052937, (31, 3519): 295.2142205791655, (31, 3536): 293.92787776920704, (31, 3545): 291.55404612471455, (31, 3548): 293.22431216611227, (31, 3572): 293.5320588195652, (31, 3581): 296.14946527382256, (31, 3583): 295.809703517639, (31, 3601): 293.27406484797274, (31, 3656): 296.71922711114604, (31, 3669): 302.3371615416794, (31, 3670): 301.3317451775852, (31, 3695): 306.5780785566218, (31, 3696): 305.6115789822847, (31, 3782): 288.8090999855839, (31, 3792): 290.78826955359574, (31, 3989): 884.4085371467854, (31, 4008): 891.6896921150365, (31, 4031): 890.7042408565545, (31, 4045): 888.6095536956241, (31, 4144): 889.4661777929813, (31, 4145): 882.6188490872494, (31, 4164): 886.7650619842443, (31, 4168): 884.7120344180018, (31, 4173): 884.3558156982997, (31, 4181): 879.9036789735313, (31, 4228): 875.2016565318344, (31, 4248): 874.0332268505775, (31, 4254): 835.3884893979155, (31, 4260): 835.4206526566387, (31, 4262): 838.098706962783, (31, 4273): 837.4562526655538, (31, 4319): 813.1593407969016, (31, 4326): 812.3273520970155, (31, 4328): 812.6402609484119, (31, 4334): 814.2231803909084, (31, 4335): 813.6330123788256, (31, 4372): 757.4659158953326, (31, 4413): 776.7901124214312, (31, 4434): 757.1006949958131, (31, 4447): 761.4573253919921, (31, 4452): 757.1462725104013, (31, 4463): 703.3983216939564, (31, 4465): 705.5267917277159, (31, 4619): 774.037762073552, (31, 4645): 780.0510151902657, (31, 4657): 778.5574555411462, (31, 4666): 775.9359421818688, (31, 4676): 779.578839757924, (31, 4678): 780.7129439156279, (31, 4689): 777.4233702322432, (31, 4704): 795.3975971703773, (31, 4726): 823.6568596771695, (31, 4727): 823.0676688623794, (31, 4730): 821.9782742891156, (31, 4731): 821.9407886966147, (31, 4734): 824.5841301151803, (31, 4735): 823.7248307550225, (31, 4736): 823.7456009499227, (31, 4737): 822.3990664327081, (31, 4738): 822.3202351923626, (31, 4756): 822.749154571185, (31, 4760): 821.2634058082291, (31, 4761): 822.1878269427804, (31, 4762): 820.0984676575154, (31, 4765): 821.3770947927376, (31, 4773): 825.1107050740632, (31, 4774): 824.0780848136351, (31, 4790): 824.7946308464624, (31, 4795): 824.4061896971493, (31, 4799): 824.0647600741784, (31, 4801): 824.6062595921193, (31, 4804): 825.2395316757226, (31, 4805): 824.9126610605948, (31, 4806): 823.1070781649585, (31, 4815): 822.0960623706643, (31, 4816): 823.8037772256883, (31, 4817): 823.5117705960196, (31, 4826): 822.8117544699757, (31, 4830): 821.7248728310426, (31, 4839): 822.9530710297796, (31, 4840): 823.231068653249, (31, 4841): 821.7857606934995, (31, 4846): 821.4748181839407, (31, 4848): 820.840347639143, (31, 4850): 821.2910144635664, (31, 4871): 816.7338572993268, (31, 4883): 821.3259018598595, (31, 4900): 819.6636070250646, (31, 4901): 818.5324168671491, (31, 4917): 764.0809054071352, (31, 4931): 759.2078070400026, (31, 4944): 765.0099112785399, (31, 4956): 759.7254080410029, (31, 4958): 758.8405105441916, (31, 4959): 757.4055082433557, (31, 4961): 761.0157812225353, (31, 4966): 758.103665462243, (31, 5207): 752.6306822892726, (31, 5272): 684.3732428479921, (31, 5283): 685.8693138633039, (31, 5287): 686.574335851901, (31, 5289): 687.1685190362828, (31, 5293): 686.2958870612159, (31, 5295): 690.7273666059805, (31, 5296): 689.6704214867012, (31, 5298): 689.0453188661523, (31, 5303): 689.4765577315026, (31, 5305): 681.461225530512, (31, 5306): 678.7723243912886, (31, 5307): 680.557193040521, (31, 5308): 681.848079068229, (31, 5313): 683.0829285822159, (31, 5314): 684.4648948665232, (31, 5317): 681.1834245886605, (31, 5319): 687.7009543667465, (31, 5324): 687.5935057557421, (31, 5326): 687.5844359719534, (31, 5348): 677.5153619407542, (31, 5351): 677.2249737459005, (31, 5399): 686.5569775810574, (31, 5413): 676.9324186575608, (31, 5422): 688.4400303494274, (31, 5445): 684.3474907549581, (31, 5448): 682.8175008571641, (31, 5456): 681.3626702601738, (31, 5467): 682.4930897832089, (31, 5624): 669.2564105048377, (31, 5671): 732.831766917427, (31, 5672): 730.8384872592201, (31, 5797): 757.4923979993574, (31, 5871): 698.5235997236088, (31, 5976): 679.7691207607745, (31, 6118): 218.96054129571843, (31, 6248): 238.10686977255065, (31, 6345): 611.9522752620474, (31, 6352): 606.1326629809798, (31, 6354): 613.210607096474, (31, 6359): 614.65841874509, (31, 6376): 607.8056617926461, (31, 6378): 612.5531107589255, (31, 6381): 614.3892569355698, (31, 6383): 610.5967801151953, (31, 6396): 614.939054122469, (31, 6399): 612.3881783501616, (31, 6408): 606.0383957280972, (31, 6409): 607.9965096664175, (31, 6419): 597.3450376481413, (31, 6422): 606.1805058195155, (31, 6423): 605.6658040040866, (31, 6424): 611.7730032414466, (31, 6439): 610.4060023343338, (31, 6464): 608.5479709840093, (31, 6465): 608.2224503395305, (31, 6469): 609.5086294760297, (31, 6470): 609.2806350102463, (31, 6472): 616.7502251856555, (31, 6480): 614.2719170035392, (31, 6486): 616.5148986317, (31, 6497): 615.6906569886874, (31, 6503): 607.49915826328, (31, 6508): 608.6773954252229, (31, 6509): 609.4694364088921, (31, 6521): 614.4630734881209, (31, 6544): 613.330047970311, (31, 6552): 605.8547850714746, (31, 6553): 604.861742236226, (31, 6554): 603.8613917579851, (31, 6578): 607.6233782067313, (31, 6582): 606.1338277231042, (31, 6601): 607.9114686574363, (31, 6609): 616.5369430789648, (31, 6610): 616.6487810302712, (31, 6611): 617.2659442491761, (31, 6614): 617.019427682318, (31, 6615): 617.0474643400454, (31, 6616): 617.5036540483372, (31, 6617): 617.2542573768723, (31, 6618): 618.1295048694234, (31, 6619): 616.2299539346963, (31, 6620): 617.2640983775702, (31, 6621): 616.387264349374, (31, 6622): 616.7600717224179, (31, 6623): 616.639488752431, (31, 6624): 615.628900654724, (31, 6625): 615.6169612597594, (31, 6626): 616.3013605252544, (31, 6627): 617.0527696630292, (31, 6628): 616.8303912872964, (31, 6629): 615.535567239207, (31, 6630): 615.3374677176147, (31, 6632): 615.5963740757154, (31, 6634): 614.2761091266923, (31, 6635): 616.2315013678198, (31, 6636): 617.4595095877592, (31, 6637): 614.3750596477267, (31, 6638): 615.1828222824481, (31, 6639): 616.980225654311, (31, 6640): 615.4566386257701, (31, 6641): 616.1639633250475, (31, 6642): 615.0246984524535, (31, 6643): 616.4004996104669, (31, 6645): 616.2235049266583, (31, 6646): 618.0369227917049, (31, 6647): 615.3711699504614, (31, 6653): 617.0926280661861, (31, 6655): 617.0772629453063, (31, 6658): 614.110353525539, (31, 6662): 614.7880050801679, (31, 6819): 564.1647576051424, (31, 6996): 576.9934837186308, (31, 7059): 588.3140179440971, (31, 7187): 563.9389014143417, (31, 7304): 542.3282777716365, (31, 7528): 573.554681142504, (31, 7720): 642.7977906783543, (31, 7793): 640.6065101797894, (31, 7807): 641.7869361286778, (31, 7808): 640.0942046747083, (31, 7831): 620.8340881301368, (31, 7850): 632.6729139196856, (31, 7852): 630.5844448285424, (31, 8012): 640.8450654754289, (31, 8125): 645.2899794553646, (31, 8208): 663.4559677140587, (31, 8392): 625.6591782163031, (31, 8651): 510.1112164792769, (31, 9088): 565.7805028437068, (31, 9443): 473.70086370725784, (31, 9444): 475.2378177454114, (31, 9828): 421.3848869921152, (31, 9868): 421.8417153829698, (31, 10180): 646.1108742684497, (31, 10256): 675.0349651701927, (31, 10276): 662.2094277061427, (31, 10378): 667.7079498141944, (31, 10676): 634.0128258057852, (31, 10714): 614.2703092255472, (31, 10730): 619.443438030372, (31, 10862): 587.3926068256783, (31, 10881): 591.8699843661979, (31, 10883): 591.1613446623593, (31, 10885): 586.4841812138155, (31, 10891): 590.0618398784848, (31, 10909): 590.1735920716627, (31, 10911): 591.3212952503774, (31, 10913): 590.1201549124339, (31, 10915): 590.341918654495, (31, 10919): 591.1901124204878, (31, 11037): 554.826694997579, (31, 11039): 545.8125302840723, (31, 11516): 955.431417311893, (31, 11856): 814.9364816889725, (31, 11857): 813.6742869936744, (31, 11861): 814.3426445236643, (31, 11881): 813.3161999222054, (31, 11902): 808.2263752261158, (31, 11911): 807.4684072093585, (31, 11914): 808.1047680933764, (31, 11922): 811.8299837318583, (31, 11924): 813.071869422553, (31, 11926): 811.6154220108536, (31, 11950): 814.682978451248, (31, 11963): 819.4478930625568, (31, 11983): 816.438549900373, (31, 11985): 821.8250797983546, (31, 12009): 821.0898738564051, (31, 12010): 817.6608232650107, (31, 12018): 818.2440883547116, (31, 12020): 819.134978818944, (31, 12021): 819.7164746472516, (31, 12024): 822.9508135435127, (31, 12025): 821.8181848590054, (31, 12027): 821.0621644494078, (31, 12031): 817.09365287507, (31, 12032): 818.18844509724, (31, 12035): 820.9171824902014, (31, 12041): 822.1088593811164, (31, 12045): 777.3379978807735, (31, 12145): 798.2745411038651, (31, 12275): 886.6542553617369, (31, 12294): 877.8901854204465, (31, 12358): 904.784292946035, (31, 12463): 915.1776343800381, (31, 12465): 914.8640940633386, (31, 12482): 919.4648784861735, (31, 12503): 918.8237465836555, (31, 12506): 920.06928239792, (31, 12549): 917.3840646011271, (31, 12559): 916.4332881994625, (31, 12569): 917.4506736936769, (31, 12572): 918.3872404467885, (31, 12574): 916.431187111369, (31, 12576): 918.466293325401, (31, 12591): 918.2401223334982, (31, 12608): 925.7897755609077, (31, 12696): 913.6784573718521, (31, 12710): 920.7334672083922, (31, 12728): 917.3057202977217, (31, 12766): 713.0402933737145, (31, 12771): 703.4951144148939, (31, 12790): 702.2569432467016, (31, 12795): 699.4450681123209, (31, 12797): 687.2839509370723, (31, 12798): 688.9196786250916, (31, 12811): 698.5042487489226, (31, 12830): 695.3411181235482, (31, 12848): 696.9140166599659, (31, 12850): 697.6631976737987, (31, 12852): 694.8557274417514, (31, 12854): 693.3862072749743, (31, 12859): 698.3504897578529, (31, 12861): 690.5242083891227, (31, 12865): 700.3516783017676, (31, 12866): 699.5661955538807, (31, 12867): 702.5357102973554, (31, 12874): 701.0994540135227, (31, 12875): 702.198433676987, (31, 12881): 697.6741146739578, (31, 12883): 699.4876206939712, (31, 12885): 703.1699198033, (31, 12888): 698.6256512247888, (31, 12889): 698.1957722430401, (31, 12892): 701.4261429797845, (31, 12893): 698.7131381396381, (31, 12896): 699.5676386472529, (31, 12906): 701.2935143555272, (31, 13018): 688.9086925938706, (31, 13071): 689.2800178443447, (31, 13131): 676.7204537351508, (31, 13146): 686.2028585794827, (31, 13159): 674.0656488134633, (31, 13193): 674.7867591837987, (31, 13198): 657.5082485452095, (31, 13292): 676.8577319008468, (31, 13296): 682.0667979950764, (31, 13406): 647.6813186184864, (31, 13407): 647.1934858475967, (31, 13417): 646.473837179171, (31, 13418): 648.3898980664306, (31, 13438): 655.3391344461589, (31, 13442): 656.6282694644377, (31, 13443): 655.2293175227802, (31, 13764): 540.9351988579875, (31, 13766): 542.6884181477161, (31, 13771): 541.6003228999322, (31, 13783): 538.451642899669, (31, 13784): 544.3371435315911, (31, 13792): 539.1907388474718, (31, 13824): 537.3668343069529, (31, 14017): 544.4718935481533, (31, 14870): 598.205842939939, (31, 14997): 555.2218475961787, (31, 15000): 555.4468045304683, (31, 15003): 556.7288890930029, (31, 15006): 559.3032065692518, (31, 15007): 560.5491061618391, (31, 15056): 560.5060840752776, (31, 15063): 559.4231462267029, (31, 15069): 559.0688175602669, (31, 15076): 560.7688273451188, (31, 15086): 556.8285953094272, (31, 15087): 555.5274650449808, (31, 15111): 551.7686309527506, (31, 15116): 553.928426015809, (31, 15722): 521.0322166704029, (31, 15998): 500.38076249496623, (31, 16073): 340.3925801798198, (31, 16939): 81.82103150262215, (31, 16940): 83.31352769316894, (31, 16951): 82.95252693767115, (31, 16963): 82.46887717689519, (31, 16965): 80.11589068242573, (31, 16969): 81.43341111807281, (31, 16970): 81.35106238937533, (31, 16971): 83.42148298450151, (31, 16973): 84.05558444783624, (31, 16974): 79.65859254817087, (31, 16976): 80.88669105350534, (31, 16978): 82.23651924125963, (31, 16980): 79.72606778063142, (31, 16982): 80.22986839662367, (31, 17045): 138.30156491605536, (31, 17048): 138.3406866990782, (31, 17304): 863.9245961378093, (31, 17305): 862.512951375628, (31, 17330): 863.7608270665264, (31, 17334): 861.4896335426909, (31, 17343): 865.5752141550407, (31, 17345): 861.2444502289202, (31, 17347): 863.4859485005064, (31, 17351): 858.1476128143522, (31, 17372): 861.1575519697395, (31, 17373): 865.4548125201591, (31, 17377): 865.7434845373817, (31, 17382): 862.91252537512, (31, 17383): 863.491328427362, (31, 17389): 861.8074874320596, (31, 17400): 864.7154877845775, (31, 17401): 864.6835568527481, (31, 17402): 864.8679564348431, (31, 17403): 865.1375839754754, (31, 17440): 861.2404193126837, (31, 17455): 864.9730577566163, (31, 17491): 865.119600869565, (31, 17507): 860.1142949316338, (31, 17509): 861.7308505663973, (31, 17590): 856.9145773527235, (31, 17615): 848.9928297589172, (31, 17642): 850.5248180172756, (31, 17643): 850.3410251457728, (31, 17668): 848.9558678235288, (31, 17721): 845.4402848267321, (31, 17754): 860.4728287472194, (31, 17769): 860.7874119364667, (31, 17776): 854.2339280546166, (31, 17804): 863.3862689218068, (31, 17809): 864.9790368094549, (31, 17824): 864.019019048627, (31, 17837): 859.006659504918, (31, 17838): 859.0960745231658, (31, 17862): 857.8716465016788, (31, 17866): 861.2992542245157, (31, 17872): 856.7810320132879, (31, 17873): 854.1433720013057, (31, 17881): 858.1776478787066, (31, 17947): 234.05410399140223, (31, 17951): 236.79186000273324, (31, 17953): 237.68088411326923, (31, 17954): 237.73001291976976, (31, 17959): 233.98092020855248, (31, 17963): 234.34588510254076, (31, 18000): 249.79840995723094, (31, 18001): 249.60151395274414, (31, 18111): 237.50413057730864, (31, 18148): 303.1852727154602, (31, 18166): 279.3173795702552, (31, 18189): 252.05176816198767, (31, 18239): 866.3232035035232, (31, 18240): 866.2773203943108, (31, 18245): 866.4581577090199, (31, 18247): 866.0809427967785, (31, 18251): 866.4193084821105, (31, 18256): 866.7544447275505, (31, 18258): 866.339076450554, (31, 18259): 866.3963463639346, (31, 18260): 866.5308706356528, (31, 18262): 866.8067679953991, (31, 18263): 866.8437504630567, (31, 18264): 866.979334502663, (31, 18266): 866.9006855212318, (31, 18267): 867.0370859054941, (31, 18268): 867.0937809799856, (31, 18269): 867.3625218062526, (31, 18275): 867.2356215399599, (31, 18285): 866.9440157203769, (31, 18308): 864.1022208250354, (31, 18313): 863.0627910698698, (31, 18314): 863.455619056542, (31, 18315): 867.4254927821554, (31, 18316): 867.3651779866088, (31, 18317): 867.4885630039053, (31, 18320): 867.6586391643255, (31, 18321): 867.7097001498771, (31, 18322): 867.9116812064497, (31, 18324): 868.1294339496912, (31, 18325): 868.809490139583, (31, 18326): 868.5578362280158, (31, 18327): 867.5702097028078, (31, 18329): 869.1563921596576, (31, 18330): 868.7004229518981, (31, 18331): 868.2637671140525, (31, 18332): 867.7946437194839, (31, 18333): 868.6628406573337, (31, 18336): 868.3368654488892, (31, 18337): 868.5915459316537, (31, 18403): 868.0366084029611, (31, 18432): 857.6066748465479, (31, 18451): 864.6825286212363, (31, 18466): 871.6134361407301, (31, 18481): 867.698919667662, (31, 18483): 867.6734916169215, (31, 18484): 867.3184394127278, (31, 18485): 866.27352827013, (31, 18486): 867.3633164015839, (31, 18487): 866.5206413589225, (31, 18489): 867.1776564721594, (31, 18490): 868.1120739194464, (31, 18491): 868.5221692485258, (31, 18492): 865.6245553959866, (31, 18493): 867.2455376746979, (31, 18494): 866.9914604561941, (31, 18495): 867.8100343433588, (31, 18496): 867.3606982698166, (31, 18497): 866.3479498379921, (31, 18498): 866.4528804721307, (31, 18499): 867.0827289062911, (31, 18501): 866.6684303113528, (31, 18502): 866.2679798062745, (31, 18503): 865.9323094894421, (31, 18504): 867.5010972151899, (31, 18506): 866.7951893643267, (31, 18507): 866.4260859879176, (31, 18508): 867.0178935422742, (31, 18509): 867.0481798172699, (31, 18510): 865.975091764364, (31, 18511): 867.4142215772216, (31, 18512): 866.8941661455482, (31, 18515): 867.5728947267372, (31, 18516): 867.6811884602577, (31, 18517): 867.2079532305111, (31, 18518): 867.9938932224944, (31, 18519): 867.5745451993132, (31, 18520): 866.8705918853473, (31, 18522): 869.2414696255905, (31, 18523): 869.3556419455389, (31, 18532): 869.9549154895764, (31, 18535): 868.7364607385999, (31, 18537): 868.0580126297665, (31, 18539): 868.2133225303212, (31, 18540): 868.3064456615652, (31, 18541): 868.652018209088, (31, 18542): 868.8689733854408, (31, 18543): 867.801509895271, (31, 18546): 868.3515493261827, (31, 18555): 869.4171073261374, (31, 18556): 869.6279004134312, (31, 18565): 869.9100033627232, (31, 18567): 870.2700689503625, (31, 18568): 869.6683131088287, (31, 18577): 873.8250153596491, (31, 18583): 873.0600641491619, (31, 18605): 873.8519533327387, (31, 18608): 870.724398677883, (31, 18616): 877.7382626997238, (31, 18618): 881.0862430262113, (31, 18625): 879.7782983686092, (31, 18645): 876.7792260954662, (31, 18646): 877.6026218767615, (31, 18653): 875.01421461363, (31, 18654): 877.6826691822895, (31, 18655): 875.965106919047, (31, 18666): 886.4129248557762, (31, 18837): 871.3433987843162, (31, 18974): 863.9800793109057, (31, 18999): 866.4167516300657, (31, 19000): 867.4132736729013, (31, 19174): 818.3943033319557, (31, 19342): 838.1811636345643, (31, 19455): 826.9429586028742, (31, 19555): 777.4900838823961, (31, 19564): 780.3887198599682, (31, 19573): 778.271698895593, (31, 19586): 777.329512044627, (31, 19605): 778.1330059549314, (31, 19611): 779.5665238717711, (31, 19614): 778.9256681660606, (31, 19641): 802.9368997173686, (31, 19702): 802.4977869188618, (31, 19713): 800.745532571155, (31, 19731): 769.356882848064, (31, 19819): 819.3497684192428, (31, 19893): 757.5592047684987, (31, 19899): 767.1209162728045, (31, 19929): 760.4494174718415, (31, 19951): 780.8575965502872, (31, 19962): 761.3948120380278, (31, 19970): 767.3492132171942, (31, 19971): 767.1057261960042, (31, 19972): 765.1353448859742, (31, 19975): 764.5613036912998, (31, 19978): 786.7747335017056, (31, 19987): 787.3652198178479, (31, 19989): 781.7067800087817, (31, 20039): 788.521943635756, (31, 20043): 791.2179880083993, (31, 20047): 789.6961075752973, (31, 20052): 783.1640058583356, (31, 20054): 783.5025898236396, (31, 20085): 814.1882219393211, (31, 20104): 816.0466835659264, (31, 20132): 804.3363192277943, (31, 20203): 753.2090300614171, (31, 20280): 749.7972650379603, (31, 20285): 748.7466131021071, (31, 20290): 751.0065609486355, (31, 20297): 749.1584762479727, (31, 20309): 785.6849788789322, (31, 20453): 817.9070249980783, (31, 20485): 737.419995592357, (31, 20520): 732.7827879626903, (31, 20526): 729.8143088403071, (31, 20698): 505.24021549393547, (31, 20868): 450.04536916894455, (31, 21042): 696.4657113983404, (31, 21057): 709.6336423248782, (31, 21066): 703.0302238403591, (31, 21075): 700.770241737063, (31, 21093): 697.2487140357255, (31, 21098): 706.2930145745959, (31, 21127): 697.4386422040627, (31, 21130): 699.8207635701759, (31, 21144): 699.6436626023313, (31, 21146): 696.5793868431098, (31, 21147): 699.4824914718804, (31, 21148): 701.6977863641455, (31, 21153): 697.0195612863848, (31, 21293): 717.995727420151, (31, 21426): 716.4622630276888, (31, 21442): 730.7188843766845, (31, 21451): 732.0847698903917, (31, 21466): 723.4674289996613, (31, 21469): 725.4991108332791, (31, 21471): 722.4406477271608, (31, 21473): 724.1001862114798, (31, 21475): 722.5936069677954, (31, 21482): 726.8479181308314, (31, 21484): 726.3904672786927, (31, 21488): 725.2170966359611, (31, 21494): 722.4891526808536, (31, 21498): 724.0268952417905, (31, 21500): 721.5201593440621, (31, 21514): 725.3046950949253, (31, 21537): 720.8742776058908, (31, 21662): 726.8961468622467, (31, 21691): 718.8354237997346, (31, 21757): 705.2008542253653, (31, 21777): 670.398829407511, (31, 21778): 668.3652235487657, (31, 21779): 669.3877215665049, (31, 21790): 672.8108762046882, (31, 21802): 672.4817603120528, (31, 21824): 674.4828346630193, (31, 21874): 669.7758272578175, (31, 21879): 668.3679975551582, (31, 21983): 678.0873173082857, (31, 22002): 699.2516101861314, (31, 22132): 687.9682293214721, (31, 22261): 413.02900379502813, (31, 22298): 418.1872193499057, (31, 22339): 399.3098688441378, (31, 22508): 451.0813842663803, (31, 22841): 294.99007811833235, (31, 22842): 293.96306884910814, (31, 22874): 289.3041511263781, (31, 22941): 292.9224767353802, (31, 22956): 292.7191575869991, (31, 22960): 295.39676184189057, (31, 22968): 282.00129614691514, (31, 22970): 284.2362447544592, (31, 22974): 275.6966681501058, (31, 22980): 276.50699261696536, (31, 23025): 263.57375010469474, (31, 23028): 260.73016255930855, (31, 23081): 246.17182599318966, (31, 23104): 222.4917220706896, (31, 23147): 254.04461805188967, (31, 23298): 760.146045253157, (31, 23376): 754.2810716962028, (31, 23381): 750.3980645792781, (31, 23529): 763.5895383762811, (31, 23556): 760.2452336241826, (31, 23718): 756.8412960542383, (31, 24001): 794.9072073357469, (31, 24094): 805.2153118938676, (31, 24129): 811.0273671474814, (31, 24174): 798.7531430654604, (31, 24235): 811.533135573573, (31, 24259): 817.2129509433779, (31, 24260): 816.7776266306893, (31, 24261): 815.5497181336015, (31, 24305): 823.8903395269889, (31, 24306): 824.9880096713131, (31, 24307): 823.3109112525599, (31, 24308): 809.6326723905026, (31, 24498): 838.8413011834907, (31, 24499): 838.9618354915616, (31, 24500): 837.8969029456389, (31, 24668): 830.9203447865945, (31, 24711): 845.9725765333461, (31, 24756): 849.8233938461673, (31, 24788): 851.4931147180334, (31, 24809): 845.0361386806794, (31, 24813): 847.0500472850291, (31, 24821): 846.3868369863737, (31, 24825): 846.8862957758417, (31, 24832): 844.5922022438132, (31, 24833): 845.5824828338804, (31, 24835): 846.5714102235441, (31, 24837): 848.1402792205519, (31, 24840): 844.442195697429, (31, 24841): 845.9652658049605, (31, 24844): 844.4918365789207, (31, 24845): 845.3755919150375, (31, 24846): 845.3155290747255, (31, 24849): 845.8575057848361, (31, 24850): 847.3583964210743, (31, 24863): 833.5499251012986, (31, 24866): 835.3186529678791, (31, 24885): 837.4336702298303, (31, 24886): 837.5977107204569, (31, 24889): 841.4325868009184, (31, 24903): 842.9096239833365, (31, 24909): 836.4255007703731, (31, 24999): 912.1453428218297, (31, 25019): 909.9602052935735, (31, 25028): 911.151295554514, (31, 25137): 749.4720365050705, (31, 25145): 751.7705226453238, (31, 25208): 774.4075066204462, (31, 25233): 771.1789922147614, (31, 25371): 752.0666670025447, (31, 25377): 746.2917436726555, (31, 25828): 632.0846501427143, (31, 25851): 616.1037023006035, (31, 25874): 632.155816839618, (31, 25898): 638.2962471498187, (31, 25946): 630.3917551737201, (31, 26047): 664.2629945389224, (31, 26066): 711.2338574406674, (31, 26197): 681.9498731762181, (31, 26212): 572.2597808813333, (31, 26253): 566.3021258660494, (31, 26254): 568.5662263434876, (31, 26257): 570.6705606634174, (31, 26258): 567.5054589055268, (31, 26260): 569.1311480766753, (31, 26266): 566.8102061523086, (31, 26267): 568.742728445341, (31, 26271): 568.8142604813497, (31, 26304): 589.8692079708825, (31, 26305): 589.6865590361277, (31, 26363): 624.920510260157, (31, 26441): 435.38572162082517, (31, 26442): 435.3077485352791, (31, 26450): 438.1313690387712, (31, 26459): 440.97096034281645, (31, 26462): 441.7538593295149, (31, 26467): 434.0525622756065, (31, 26471): 434.8425684970046, (31, 26472): 434.67553469206115, (31, 26473): 434.382284386948, (31, 26476): 431.7456516574178, (31, 26485): 438.3370326386335, (31, 26493): 436.9053740518141, (31, 26524): 441.7891491108077, (31, 26525): 441.35841591647437, (31, 26556): 436.0171882542136, (31, 26560): 438.51998851914897, (31, 26561): 440.7037773761096, (31, 26564): 436.122835534894, (31, 26569): 440.3659582639878, (31, 26570): 440.1762125096205, (31, 26573): 438.560636639032, (31, 26581): 437.5681712474188, (31, 26583): 438.8011076198242, (31, 26593): 436.22418169512395, (31, 26837): 432.4322809824985, (31, 26844): 431.1848721995354, (31, 26863): 431.31857919547826, (31, 26893): 426.57806994921526, (31, 26902): 424.77124461715584, (31, 26905): 428.95779600304513, (31, 26912): 426.8077930901326, (31, 26921): 429.20374319493675, (31, 26922): 429.30215169299174, (31, 27212): 484.6136316111371, (31, 27218): 488.7555033791359, (31, 27239): 481.9576269069504, (31, 27257): 482.013007945924, (31, 27274): 480.9706152623152, (31, 27279): 480.080268110518, (31, 27282): 481.35806459578504, (31, 27283): 483.0100334843192, (31, 27285): 479.7295230135168, (31, 27286): 478.9560256923084, (31, 27290): 482.27592589076767, (31, 27295): 484.7125250926365, (31, 27300): 481.1933187881419, (31, 27344): 479.6497993752688, (31, 27366): 477.09660678793364, (31, 27383): 477.2821608381704, (31, 27398): 478.468402053595, (31, 27406): 480.5333772382753, (31, 27407): 481.0623043703892, (31, 27426): 490.30516418946, (31, 27432): 493.3428287431859, (31, 27460): 492.43950687876685, (31, 27523): 459.7860653069797, (31, 27545): 457.28959769739055, (31, 27602): 423.74038243224135, (31, 27606): 424.88737726985556, (31, 27646): 430.6673212404776, (31, 27667): 423.74836188076904, (31, 27672): 424.2705212715535, (31, 27674): 424.8904365790719, (31, 27688): 427.39385916918206, (31, 27692): 422.07963941509337, (31, 27693): 422.91912149468106, (31, 27705): 421.9726268677743, (31, 27712): 420.71242112685, (31, 27786): 462.6968114135466, (31, 27790): 478.8874679205628, (31, 27791): 481.08272560518753, (31, 27795): 462.6798713175116, (31, 27801): 473.4679963111215, (31, 27813): 460.45802743748436, (31, 27816): 463.9961478475874, (31, 27823): 473.99997163424626, (31, 27830): 468.111646507733, (31, 27884): 432.9660840246649, (31, 27885): 432.0998393496479, (31, 27896): 433.0252494682157, (31, 27919): 433.99637114110345, (31, 27922): 432.5342500074843, (31, 27930): 433.9367735905821, (31, 27934): 433.090075985776, (31, 27935): 432.138780216247, (31, 27948): 377.66562034677656, (31, 27951): 391.65999717455946, (31, 28061): 330.18044114698836, (31, 28290): 250.73874411493713, (31, 28292): 245.69108593628204, (31, 28293): 249.46829962864447, (31, 28295): 247.8525415724577, (31, 28296): 249.60124881866898, (31, 28297): 253.1780781555754, (31, 28302): 251.65333524774226, (31, 28310): 208.80589569760687, (31, 28313): 212.06869684444493, (31, 28372): 203.07780594805692, (31, 28398): 203.5732093059768, (31, 28399): 204.70770447221196, (31, 28400): 203.9899287278998, (31, 28401): 204.82616096876473, (31, 28445): 215.61064826762927, (31, 28475): 200.64803663360195, (31, 28885): 809.1419164805324, (31, 28886): 807.9184438701336, (31, 28915): 808.3658001232989, (31, 28916): 807.5967510102738, (31, 28917): 806.8912632085217, (31, 28921): 811.2963465438743, (31, 28931): 810.8668522970534, (31, 28945): 803.7035224907678, (31, 28982): 805.6120074056976, (31, 29219): 808.9985350917044, (31, 29228): 804.2202269622715, (31, 29246): 833.7109434979786, (31, 29248): 832.69628075347, (31, 29282): 826.4553793276532, (31, 29290): 837.4312481841251, (31, 29291): 835.9940122641094, (31, 29292): 837.2577565416121, (31, 29293): 834.7864904872447, (31, 29294): 836.5087445962254, (31, 29298): 834.8220868557919, (31, 29299): 834.4562548715674, (31, 29304): 832.4871441259154, (31, 29317): 826.7541634579466, (31, 29323): 826.3259682271528, (31, 29330): 829.0621995355239, (31, 29331): 830.5482366460787, (31, 29344): 808.3999172171567, (31, 29445): 751.0999482715877, (31, 29724): 334.43639178814163, (31, 29738): 334.5505813482517, (31, 29745): 335.76915411059184, (31, 29748): 343.6566122711982, (31, 29750): 347.1370137541147, (31, 29759): 342.54304625404535, (31, 29772): 343.0965141206515, (31, 29781): 343.1975199140327, (31, 29784): 339.746803725393, (31, 29790): 344.6970673067227, (31, 29811): 347.8384935078189, (31, 29817): 369.2155465367482, (31, 29818): 369.42873296413484, (31, 29929): 330.84293571146895, (31, 30039): 310.5423827471229, (31, 30066): 296.7837226255004, (31, 30116): 311.38463007679377, (31, 30238): 335.705060627308, (31, 30248): 301.35937201306996, (31, 30260): 299.149956738976, (31, 30545): 793.869595387014, (31, 30733): 742.2693598900244, (31, 30756): 726.6331748438855, (31, 30921): 752.6289437721564, (31, 31079): 623.5735958123718, (31, 31149): 616.6412173183948, (31, 31154): 616.7578856305948, (31, 31160): 616.2371700944242, (31, 31163): 615.9254199546239, (31, 31189): 594.0488422511602, (31, 31215): 595.311179702693, (31, 31259): 592.4633743975293, (31, 31262): 590.1087580356417, (31, 31430): 625.7347157841431, (31, 31568): 564.0841738445451, (31, 31751): 611.6296332658975, (32, 109): 73.78178739569941, (32, 872): 446.4920560007142, (32, 873): 449.04473358108254, (32, 877): 448.3651281735554, (32, 879): 448.77091073652934, (32, 884): 446.8325618961665, (32, 889): 448.2987927323297, (32, 891): 445.9126673222118, (32, 892): 450.69202768054026, (32, 894): 450.2558740677412, (32, 896): 447.3361094593408, (32, 903): 448.7797516895035, (32, 909): 443.52143999792776, (32, 910): 444.28749963991874, (32, 912): 442.6596209479687, (32, 913): 440.96033035535436, (32, 916): 439.8670802964977, (32, 926): 444.7896274248474, (32, 927): 443.87591597075885, (32, 948): 444.9422942634006, (32, 961): 445.29550722692505, (32, 962): 445.406520067148, (32, 963): 445.5892348471594, (32, 967): 449.74541524595594, (32, 974): 449.0306416559198, (32, 998): 450.98539624127926, (32, 1014): 503.47381081793344, (32, 1086): 433.0626065541855, (32, 1087): 431.904734784865, (32, 1089): 429.9954882510635, (32, 1090): 431.1362365511523, (32, 1092): 434.8039138174965, (32, 1097): 432.1721215587069, (32, 1107): 436.101451837975, (32, 1387): 48.95815211260716, (32, 1554): 24.590303344240223, (32, 1827): 568.898922702543, (32, 1828): 569.0434621583048, (32, 1829): 569.5214908267025, (32, 1830): 569.7135528172689, (32, 1831): 569.8361525335607, (32, 1832): 569.5034200439095, (32, 1833): 569.4318085730335, (32, 1836): 569.0220547675959, (32, 1841): 570.809685998455, (32, 1843): 570.1237425225463, (32, 1844): 570.5307706168061, (32, 1845): 569.8034989054988, (32, 1847): 566.8592120081887, (32, 1848): 567.8064986851668, (32, 1849): 572.347378372274, (32, 1850): 572.7177024678325, (32, 1851): 568.8040195589753, (32, 1852): 569.1095293532093, (32, 1854): 569.3757869777187, (32, 1856): 567.0376587141628, (32, 1857): 567.870897005506, (32, 1858): 571.7520494856647, (32, 1861): 569.665086788, (32, 1866): 567.1823207941972, (32, 1867): 570.6577763457237, (32, 1868): 569.914255662883, (32, 1870): 570.7602788591205, (32, 1871): 570.3348755393349, (32, 1875): 569.1681395366974, (32, 1880): 567.4153548005858, (32, 1882): 568.0310742594513, (32, 1883): 572.485279643329, (32, 1889): 567.5092611879678, (32, 1893): 569.1872045758416, (32, 1894): 568.4695963154031, (32, 1899): 566.7740416820162, (32, 1900): 567.1730541735938, (32, 1902): 570.31592671107, (32, 1905): 571.3089163098447, (32, 1907): 568.1952330531259, (32, 1910): 568.213385029844, (32, 1917): 572.3083908027238, (32, 1920): 568.05029346453, (32, 1935): 570.9716175714253, (32, 1937): 571.7634172212231, (32, 1946): 564.7970504729662, (32, 1949): 565.468941718964, (32, 1950): 563.2839679306004, (32, 1951): 564.4679030843027, (32, 1952): 566.082631177407, (32, 1953): 565.9525004313331, (32, 1954): 565.7355120258287, (32, 1958): 565.4984152694952, (32, 1960): 566.9924403660735, (32, 1968): 567.5806333763067, (32, 1969): 570.679323652699, (32, 1974): 569.9096463804692, (32, 1975): 570.0527352608989, (32, 1979): 567.8649495348269, (32, 1980): 568.1772809526204, (32, 1981): 568.4380891499181, (32, 1985): 568.7637299961907, (32, 1994): 563.2811353495731, (32, 2011): 568.1565774841077, (32, 2019): 575.4219944711555, (32, 2020): 574.4647607307463, (32, 2029): 571.2867932231616, (32, 2030): 573.7939296090336, (32, 2032): 571.0040004109571, (32, 2033): 572.4605642979952, (32, 2034): 572.6620224282566, (32, 2036): 570.3709107408667, (32, 2037): 570.919114411963, (32, 2038): 570.112159944087, (32, 2042): 580.4092716747463, (32, 2050): 571.6611242756455, (32, 2051): 571.7614263894175, (32, 2053): 571.9253801015851, (32, 2054): 572.8448888079431, (32, 2066): 571.0174914623184, (32, 2067): 570.8959937308648, (32, 2071): 561.4430051172848, (32, 2072): 562.9510358396989, (32, 2073): 557.6749814042905, (32, 2074): 557.6032140877005, (32, 2080): 555.1481252677085, (32, 2082): 563.8200072335299, (32, 2083): 564.5849923731294, (32, 2089): 562.5650440939473, (32, 2090): 563.2367717512279, (32, 2092): 561.9945944697346, (32, 2098): 555.9179653571406, (32, 2099): 557.0426328018217, (32, 2101): 555.959413691751, (32, 2102): 560.2480572522805, (32, 2103): 558.9883754122402, (32, 2104): 558.4031614563718, (32, 2106): 565.2670556746212, (32, 2112): 556.7339250220895, (32, 2113): 560.9932978246196, (32, 2114): 562.4066798789113, (32, 2117): 566.1063006799699, (32, 2123): 551.2661651238765, (32, 2124): 552.1536108251607, (32, 2134): 550.1793264038291, (32, 2138): 552.5678886919582, (32, 2141): 550.3159101725487, (32, 2148): 553.7846387969811, (32, 2150): 548.2597607901241, (32, 2151): 549.3517477582542, (32, 2152): 547.9163366879686, (32, 2153): 553.8752059170822, (32, 2154): 550.0646956382482, (32, 2155): 550.0127636601508, (32, 2156): 549.0637557643407, (32, 2157): 551.3560095955534, (32, 2160): 554.847332324923, (32, 2161): 547.9780096356671, (32, 2162): 554.8621300696935, (32, 2163): 553.5428549975, (32, 2164): 553.5935076148467, (32, 2168): 549.7307800436147, (32, 2172): 551.5624223412569, (32, 2174): 549.5165218198232, (32, 2178): 552.5858476215412, (32, 2179): 552.0959323250224, (32, 2183): 552.7561243638767, (32, 2185): 552.9452561377269, (32, 2186): 552.1662595023134, (32, 2190): 554.7845360062056, (32, 2192): 553.427881751833, (32, 2193): 552.9304821443492, (32, 2194): 551.5456994295992, (32, 2195): 551.6312433501494, (32, 2197): 553.8653323178164, (32, 2205): 552.3343225166723, (32, 2207): 550.2533866054293, (32, 2208): 551.4746263738268, (32, 2212): 552.7111424776912, (32, 2214): 529.9975378857188, (32, 2225): 534.0796106360897, (32, 2231): 521.4989666984615, (32, 2278): 549.4836533004051, (32, 2284): 552.7647122278571, (32, 2285): 552.5737520247633, (32, 2291): 548.3668577770419, (32, 2292): 547.3634068153705, (32, 2307): 550.9890378666312, (32, 2313): 548.2171482288697, (32, 2317): 544.6552858450867, (32, 2319): 548.482250163948, (32, 2321): 550.0299164553122, (32, 2323): 549.4111142050511, (32, 2326): 553.4724037849916, (32, 2327): 552.2588621319551, (32, 2329): 551.4765106543156, (32, 2330): 550.6904645345375, (32, 2332): 552.8988032649021, (32, 2344): 549.1636708231466, (32, 2346): 549.4177429987893, (32, 2361): 546.3748252467989, (32, 2368): 562.0088789993767, (32, 2374): 563.5836035017148, (32, 2375): 563.8778923520129, (32, 2377): 558.9740062866872, (32, 2378): 564.8535341959633, (32, 2379): 565.2807979755922, (32, 2380): 565.5243656093756, (32, 2383): 560.0365905077056, (32, 2385): 560.6530296465074, (32, 2395): 560.4612894055782, (32, 2397): 564.8629492460268, (32, 2398): 557.4458084456206, (32, 2399): 558.9950409443817, (32, 2400): 558.6092613424225, (32, 2402): 562.1575747195362, (32, 2403): 563.2311722981224, (32, 2404): 563.3812491710953, (32, 2405): 560.9077281269716, (32, 2407): 562.7395849983686, (32, 2408): 564.1303127222587, (32, 2409): 561.609768329549, (32, 2411): 563.7376530652274, (32, 2412): 563.2628929298232, (32, 2413): 564.2141894953425, (32, 2414): 562.85251514122, (32, 2422): 563.5906945801199, (32, 2424): 563.4530624789156, (32, 2426): 563.5810276269664, (32, 2433): 561.7857706976697, (32, 2436): 561.5922487551184, (32, 2437): 555.2504880995303, (32, 2440): 556.5561222210947, (32, 2445): 586.9532934654377, (32, 2447): 583.2670727388872, (32, 2454): 586.4495394969313, (32, 2455): 586.3784536556311, (32, 2460): 576.8272297571804, (32, 2461): 578.0603856031606, (32, 2471): 599.1287896740267, (32, 2492): 588.3234399047858, (32, 2511): 576.8236139182133, (32, 2523): 582.7412167620507, (32, 2525): 581.8241047342783, (32, 2535): 579.0143745557845, (32, 2537): 577.0180491642187, (32, 2538): 578.1431557573729, (32, 2539): 578.7637977857989, (32, 2540): 579.9519117276728, (32, 2542): 581.8330395153951, (32, 2559): 609.5351748823877, (32, 2575): 608.2536671596033, (32, 2599): 559.0336226402126, (32, 2600): 570.1006607335484, (32, 2607): 562.7738576907245, (32, 2627): 587.3909012887702, (32, 2647): 593.9582284978494, (32, 2674): 589.6301625360081, (32, 2681): 589.5229163688495, (32, 2683): 591.9874133675102, (32, 2686): 588.4731941459996, (32, 2689): 626.0952993382565, (32, 2690): 626.4389790844077, (32, 2713): 638.5605375645142, (32, 2714): 639.8686899642693, (32, 2715): 640.743884674277, (32, 2739): 639.7651090818594, (32, 2740): 632.3321991987589, (32, 2741): 632.6337154733338, (32, 2749): 639.2798663241981, (32, 2750): 639.3096030201729, (32, 2752): 639.8235341391962, (32, 2755): 640.6712175611668, (32, 2758): 640.6743318924542, (32, 2759): 640.5674580998143, (32, 2769): 639.2697263631263, (32, 2771): 634.2450264747815, (32, 2779): 636.2942571756679, (32, 2784): 627.1478883855942, (32, 2800): 630.6994614763863, (32, 2802): 631.5712419902414, (32, 2803): 631.0134509718017, (32, 2804): 630.3356030366288, (32, 2805): 632.9868108442391, (32, 2807): 632.7060697977116, (32, 2809): 632.8812680531406, (32, 2812): 626.6397565112019, (32, 2814): 634.0832637790511, (32, 2817): 636.3195719865985, (32, 2819): 632.2700752491203, (32, 2823): 629.1501565118076, (32, 2832): 634.4043510732682, (32, 2836): 630.3912671249612, (32, 2839): 632.4647438724116, (32, 2841): 635.4796159317132, (32, 2843): 634.8174859284542, (32, 2846): 632.0967033836542, (32, 2849): 635.4114787431198, (32, 2852): 634.3556833883983, (32, 2853): 635.9113780084014, (32, 2876): 637.3720368582447, (32, 2877): 640.745630987645, (32, 2885): 643.8782282224827, (32, 2918): 631.2906348455875, (32, 2921): 632.9465483488505, (32, 2925): 624.454920239813, (32, 2926): 621.2099537751026, (32, 2930): 629.6916160062569, (32, 2931): 625.6705792929619, (32, 2938): 631.697847302364, (32, 2940): 633.9108255668673, (32, 2947): 628.6683402525069, (32, 2949): 628.7672273557123, (32, 2950): 629.7765630602611, (32, 2952): 629.1002402546114, (32, 2958): 628.8080800221302, (32, 2959): 629.0271116744785, (32, 2960): 630.7076677414187, (32, 2961): 630.1476215191201, (32, 2963): 628.4480984258759, (32, 2968): 629.1142973987645, (32, 2976): 628.03191327408, (32, 2981): 617.8015789318048, (32, 2982): 617.8958334706147, (32, 2984): 617.331108901136, (32, 3003): 616.6691581010172, (32, 3046): 602.5518306476777, (32, 3050): 611.9802843029356, (32, 3051): 612.3358142742303, (32, 3053): 611.0461385431261, (32, 3069): 620.1123141491324, (32, 3071): 609.6286846463217, (32, 3080): 644.6819384706196, (32, 3199): 617.3695540203862, (32, 3200): 616.1430547451574, (32, 3205): 625.4171290865896, (32, 3209): 617.0060389920426, (32, 3215): 615.9746011975454, (32, 3217): 614.1417143757333, (32, 3249): 615.8638014151077, (32, 3263): 629.6021302369533, (32, 3289): 619.4946358921371, (32, 3301): 620.618659362497, (32, 3302): 619.7056381899546, (32, 3307): 618.8093482435776, (32, 3310): 621.4091584544668, (32, 3391): 636.5138653872289, (32, 3509): 311.4273043885017, (32, 3510): 310.1431418681718, (32, 3511): 310.5458124302884, (32, 3512): 309.35497962186804, (32, 3514): 309.2673552164293, (32, 3519): 316.6550253673992, (32, 3536): 312.9020427442412, (32, 3545): 314.4706088269749, (32, 3548): 311.90863596405103, (32, 3572): 314.1790800189603, (32, 3581): 314.1286400180099, (32, 3583): 311.3928043436109, (32, 3601): 319.7676111823439, (32, 3656): 319.43423918159533, (32, 3669): 320.7643199063508, (32, 3670): 322.0684665735301, (32, 3695): 313.9413019719642, (32, 3696): 314.7735337965047, (32, 3782): 304.75293728073655, (32, 3792): 304.46958872940246, (32, 3989): 363.2418504238495, (32, 4008): 371.01980126796917, (32, 4031): 372.17637411968144, (32, 4045): 367.8329479505195, (32, 4144): 366.70316489715395, (32, 4145): 357.2049622665261, (32, 4164): 363.2998340522595, (32, 4168): 360.0846704534445, (32, 4173): 359.19673522584793, (32, 4181): 354.4557011990039, (32, 4228): 351.7623021330436, (32, 4248): 347.39884843016245, (32, 4254): 297.1302369378209, (32, 4260): 298.1060495690006, (32, 4262): 300.3446354591014, (32, 4273): 300.26546511703145, (32, 4319): 269.5547142470111, (32, 4326): 268.8663983322805, (32, 4328): 269.450393115227, (32, 4334): 270.45069114386956, (32, 4335): 269.6518491802558, (32, 4372): 205.89650056452297, (32, 4413): 229.9203852438574, (32, 4434): 204.82459812691857, (32, 4447): 207.72956158314403, (32, 4452): 205.19290857727682, (32, 4463): 160.1547387020603, (32, 4465): 161.460439979796, (32, 4619): 234.14683960422147, (32, 4645): 238.92308193583276, (32, 4657): 238.33120732787327, (32, 4666): 236.56784425033254, (32, 4676): 240.07726966131457, (32, 4678): 240.76112392525448, (32, 4689): 238.62570806606954, (32, 4704): 256.1029984155576, (32, 4726): 302.91830537656807, (32, 4727): 302.0661529269909, (32, 4730): 300.3978549077607, (32, 4731): 300.98387893578484, (32, 4734): 301.3211229234088, (32, 4735): 300.602447035314, (32, 4736): 301.08367300898345, (32, 4737): 299.7583245344163, (32, 4738): 300.01123594810804, (32, 4756): 300.90970571402676, (32, 4760): 296.2330803397534, (32, 4761): 296.5572427978086, (32, 4762): 295.1704547631636, (32, 4765): 296.6975499589289, (32, 4773): 304.5063604202926, (32, 4774): 303.87640215173985, (32, 4790): 303.9210842828186, (32, 4795): 303.1454950077507, (32, 4799): 304.31544426933897, (32, 4801): 306.29114835115377, (32, 4804): 303.2788923519269, (32, 4805): 302.64556675711464, (32, 4806): 303.7499487280669, (32, 4815): 303.0522016918169, (32, 4816): 305.12958692760793, (32, 4817): 305.7153231725223, (32, 4826): 304.3892980801865, (32, 4830): 303.24377258034787, (32, 4839): 298.7071381607672, (32, 4840): 299.52106506358103, (32, 4841): 297.78146065949267, (32, 4846): 297.1712003649341, (32, 4848): 297.0954264283477, (32, 4850): 297.88683350350607, (32, 4871): 287.595215683225, (32, 4883): 295.12208273472163, (32, 4900): 291.1091433793744, (32, 4901): 290.1381840655167, (32, 4917): 235.73016333560216, (32, 4931): 229.6608153266037, (32, 4944): 236.32067043282308, (32, 4956): 230.8718592403875, (32, 4958): 230.89748947048162, (32, 4959): 229.8876141636848, (32, 4961): 232.02134574029833, (32, 4966): 229.5034378231354, (32, 5207): 222.79753139008596, (32, 5272): 115.59947636129824, (32, 5283): 117.22507389686663, (32, 5287): 118.61908379583814, (32, 5289): 119.33853486982727, (32, 5293): 117.3662422146613, (32, 5295): 122.04916845146111, (32, 5296): 121.17118888281024, (32, 5298): 120.65996365221467, (32, 5303): 121.46120465074407, (32, 5305): 112.94785332157429, (32, 5306): 110.45101079887188, (32, 5307): 111.9835961137506, (32, 5308): 113.48207196034525, (32, 5313): 114.44929432264506, (32, 5314): 115.84797703015506, (32, 5317): 112.98247887327398, (32, 5319): 119.56111050815437, (32, 5324): 119.16779473853074, (32, 5326): 118.99385929419935, (32, 5348): 109.37710982366455, (32, 5351): 109.71639845406841, (32, 5399): 119.3836652906001, (32, 5413): 110.7938696742899, (32, 5422): 121.0322746916646, (32, 5445): 116.5454297121596, (32, 5448): 114.81362238396993, (32, 5456): 113.64504574926764, (32, 5467): 115.08901453251335, (32, 5624): 100.42126151557925, (32, 5671): 164.59149806855459, (32, 5672): 162.3892583985129, (32, 5797): 193.29149356789577, (32, 5871): 143.96738126718517, (32, 5976): 119.78908056855265, (32, 6118): 500.61464652086255, (32, 6248): 539.5410358093203, (32, 6345): 176.91619691873686, (32, 6352): 178.55918359176994, (32, 6354): 175.79791746798853, (32, 6359): 176.85327587819114, (32, 6376): 181.58156296653218, (32, 6378): 176.12637578843564, (32, 6381): 177.90285757415546, (32, 6383): 176.70640141426944, (32, 6396): 183.38327884233092, (32, 6399): 178.5181489812305, (32, 6408): 177.14314828443585, (32, 6409): 172.78498886755702, (32, 6419): 170.05145424931655, (32, 6422): 174.10547875250592, (32, 6423): 174.04357280312146, (32, 6424): 171.94848275247728, (32, 6439): 171.08052746302204, (32, 6464): 170.38301483301848, (32, 6465): 171.76224343875236, (32, 6469): 174.15636445840033, (32, 6470): 174.84907844642606, (32, 6472): 176.91000341871128, (32, 6480): 171.30022116786003, (32, 6486): 164.34186487274653, (32, 6497): 166.35834312577745, (32, 6503): 163.1006042334285, (32, 6508): 166.88535524087922, (32, 6509): 164.84443132709708, (32, 6521): 168.4937059679319, (32, 6544): 164.8788760606597, (32, 6552): 167.4603062838557, (32, 6553): 167.31442634449985, (32, 6554): 167.22180038035214, (32, 6578): 168.25939752352585, (32, 6582): 164.33327999162017, (32, 6601): 167.49984351574406, (32, 6609): 172.12303118202453, (32, 6610): 171.3317625057189, (32, 6611): 173.44774979265546, (32, 6614): 174.66711141690968, (32, 6615): 173.94697800423043, (32, 6616): 171.28883190597372, (32, 6617): 172.21813843057186, (32, 6618): 169.55986009711012, (32, 6619): 174.20188085047073, (32, 6620): 169.98360648788253, (32, 6621): 169.6591959765577, (32, 6622): 170.57823562405994, (32, 6623): 173.2381136702789, (32, 6624): 171.82721858524215, (32, 6625): 172.52376170831613, (32, 6626): 174.7694906013616, (32, 6627): 175.7950368300693, (32, 6628): 168.63869050065773, (32, 6629): 170.23338505425863, (32, 6630): 174.58235005010275, (32, 6632): 170.95540658103377, (32, 6634): 173.7049458733217, (32, 6635): 170.34717915803654, (32, 6636): 170.83957005468463, (32, 6637): 170.0248671391245, (32, 6638): 173.34349842589782, (32, 6639): 175.03903717568448, (32, 6640): 174.01125097091946, (32, 6641): 168.63244731882995, (32, 6642): 172.47363083684158, (32, 6643): 175.69379454639372, (32, 6645): 173.61462830896622, (32, 6646): 170.56606830075037, (32, 6647): 172.96987483224652, (32, 6653): 174.34659458997328, (32, 6655): 175.46309347055347, (32, 6658): 173.1910395831011, (32, 6662): 171.53533983157962, (32, 6819): 158.20795913765605, (32, 6996): 135.22902344895394, (32, 7059): 135.11336500030293, (32, 7187): 91.16561480908382, (32, 7304): 122.93902721511846, (32, 7528): 115.92706680816484, (32, 7720): 144.08188552598267, (32, 7793): 137.01977470919462, (32, 7807): 139.51903336058274, (32, 7808): 135.38484923428234, (32, 7831): 163.73609646640125, (32, 7850): 172.12806877041172, (32, 7852): 173.41258917823018, (32, 8012): 152.0899982039081, (32, 8125): 113.50217036890605, (32, 8208): 152.73482687790042, (32, 8392): 145.2698477617527, (32, 8651): 174.79799030884178, (32, 9088): 184.45788684919353, (32, 9443): 134.68374439794576, (32, 9444): 132.7220277760959, (32, 9828): 161.3055752407292, (32, 9868): 176.35366432135356, (32, 10180): 111.5920356047185, (32, 10256): 129.3393219123553, (32, 10276): 124.70365901431296, (32, 10378): 141.28902696088932, (32, 10676): 84.08969749651347, (32, 10714): 66.09715907866372, (32, 10730): 85.66457192391873, (32, 10862): 123.27698157977802, (32, 10881): 125.72107108044405, (32, 10883): 126.0449831625492, (32, 10885): 122.61298842279211, (32, 10891): 126.57812515442397, (32, 10909): 124.9255775858514, (32, 10911): 123.80189923060922, (32, 10913): 123.70396471350165, (32, 10915): 122.91846483657095, (32, 10919): 122.62877840416644, (32, 11037): 128.9313791842713, (32, 11039): 118.54985254096881, (32, 11516): 460.9494926633506, (32, 11856): 271.0930994301579, (32, 11857): 268.72476177122314, (32, 11861): 269.9147083481122, (32, 11881): 270.5403791363759, (32, 11902): 265.931729839212, (32, 11911): 266.49038874869717, (32, 11914): 266.5186617243117, (32, 11922): 269.4568862541417, (32, 11924): 270.8959460920359, (32, 11926): 269.65050396449783, (32, 11950): 273.78123544345493, (32, 11963): 277.8984904236575, (32, 11983): 277.4501415025772, (32, 11985): 279.8492691433634, (32, 12009): 281.07427099333484, (32, 12010): 277.6402711446551, (32, 12018): 278.4033277952159, (32, 12020): 278.89999347802865, (32, 12021): 279.6138857891629, (32, 12024): 282.42721025434935, (32, 12025): 281.0556735733089, (32, 12027): 280.4925145046667, (32, 12031): 277.13747488784014, (32, 12032): 277.78583665085256, (32, 12035): 281.3642682850936, (32, 12041): 279.0219546001742, (32, 12045): 242.64198092266332, (32, 12145): 262.4651805739679, (32, 12275): 370.1299643442553, (32, 12294): 365.2016526845925, (32, 12358): 390.68549464152204, (32, 12463): 402.22459322177104, (32, 12465): 402.1031457092247, (32, 12482): 403.86549263329454, (32, 12503): 403.86019978170935, (32, 12506): 404.8793940383505, (32, 12549): 400.101039814096, (32, 12559): 399.8349739696884, (32, 12569): 401.5828812399072, (32, 12572): 402.29681281392243, (32, 12574): 400.5210874441603, (32, 12576): 400.6795387717677, (32, 12591): 399.02969812396583, (32, 12608): 404.15843636844977, (32, 12696): 393.28057004855367, (32, 12710): 397.16285368286736, (32, 12728): 396.3844389565088, (32, 12766): 240.38313262939818, (32, 12771): 225.90605104819528, (32, 12790): 225.36911482522734, (32, 12795): 225.2058624147919, (32, 12797): 211.90333722318346, (32, 12798): 212.68544069384433, (32, 12811): 219.81083480572065, (32, 12830): 218.99522180054296, (32, 12848): 217.02349462777497, (32, 12850): 215.70733830635146, (32, 12852): 217.69407985978816, (32, 12854): 216.6333604978321, (32, 12859): 217.2589101074224, (32, 12861): 213.1207263356177, (32, 12865): 222.5388392880306, (32, 12866): 221.04478291967635, (32, 12867): 224.05287483802002, (32, 12874): 222.72364210232033, (32, 12875): 223.1416163304849, (32, 12881): 220.8829605566852, (32, 12883): 222.0957820847548, (32, 12885): 224.06696956626982, (32, 12888): 220.86059789492097, (32, 12889): 219.94610246786195, (32, 12892): 223.31554805455346, (32, 12893): 221.55689151734424, (32, 12896): 221.53723808706735, (32, 12906): 225.66395286615196, (32, 13018): 234.19776763620618, (32, 13071): 238.28582331594578, (32, 13131): 215.12960907127305, (32, 13146): 217.82427025184919, (32, 13159): 230.80408793546178, (32, 13193): 212.81182819674453, (32, 13198): 196.16802549894135, (32, 13292): 205.60815003767996, (32, 13296): 202.06205077782138, (32, 13406): 202.7490119224431, (32, 13407): 203.46106859552074, (32, 13417): 210.61613353938205, (32, 13418): 212.6948074354302, (32, 13438): 210.13178697426497, (32, 13442): 208.31626289967843, (32, 13443): 207.94698185065457, (32, 13764): 249.86118597504196, (32, 13766): 249.4262886495581, (32, 13771): 252.90542919913173, (32, 13783): 245.1258388149741, (32, 13784): 247.64303021040482, (32, 13792): 258.35071337905134, (32, 13824): 246.05286888223543, (32, 14017): 225.6127483130396, (32, 14870): 93.44057782053842, (32, 14997): 89.14100473375815, (32, 15000): 87.37021317336475, (32, 15003): 85.38010917299461, (32, 15006): 92.54960421206337, (32, 15007): 92.1682854134066, (32, 15056): 86.96716661397959, (32, 15063): 86.12362794479768, (32, 15069): 84.21313630258378, (32, 15076): 90.90165322980421, (32, 15086): 93.81456203931499, (32, 15087): 91.64831190547426, (32, 15111): 94.24230215561116, (32, 15116): 92.55886692289648, (32, 15722): 106.45913540651932, (32, 15998): 84.66152239407045, (32, 16073): 433.42847531280427, (32, 16939): 498.8072084725334, (32, 16940): 496.8860174859603, (32, 16951): 499.99416502770197, (32, 16963): 499.95069911990623, (32, 16965): 501.8833711023235, (32, 16969): 501.8952984570933, (32, 16970): 500.4711735209482, (32, 16971): 498.696273976008, (32, 16973): 498.91027251760903, (32, 16974): 502.9783566206569, (32, 16976): 500.3989866999468, (32, 16978): 498.98551859224494, (32, 16980): 500.77406051777984, (32, 16982): 503.31123269043167, (32, 17045): 587.6374414472645, (32, 17048): 590.1240075776735, (32, 17304): 334.12096289254663, (32, 17305): 334.1401827758627, (32, 17330): 334.9027087704416, (32, 17334): 331.54674964233135, (32, 17343): 336.9134238021823, (32, 17345): 332.7484360946421, (32, 17347): 335.5796174432631, (32, 17351): 328.3497826985015, (32, 17372): 331.77056473289554, (32, 17373): 336.57928118732787, (32, 17377): 337.02192649621594, (32, 17382): 334.16279137867906, (32, 17383): 334.26353634607665, (32, 17389): 332.6799053880558, (32, 17400): 335.3806452486046, (32, 17401): 335.1205535991133, (32, 17402): 335.6733760629523, (32, 17403): 336.06241874379407, (32, 17440): 334.3268808824527, (32, 17455): 337.2620195744368, (32, 17491): 338.48930117272795, (32, 17507): 326.8869299524698, (32, 17509): 328.1137940995263, (32, 17590): 328.7629107288012, (32, 17615): 312.00094489825074, (32, 17642): 314.18091934199686, (32, 17643): 314.5274651969376, (32, 17668): 311.6379118557929, (32, 17721): 305.3072299805894, (32, 17754): 319.21287082934697, (32, 17769): 325.9693145142382, (32, 17776): 322.1369543514519, (32, 17804): 328.25581011735864, (32, 17809): 329.8011753946021, (32, 17824): 328.0113793798406, (32, 17837): 327.2479605687388, (32, 17838): 328.13361946180856, (32, 17862): 327.33688019713264, (32, 17866): 330.261584423515, (32, 17872): 325.79761643430453, (32, 17873): 323.7309540182207, (32, 17881): 327.01152366388993, (32, 17947): 335.0065845215741, (32, 17951): 332.2165103102621, (32, 17953): 331.3352612389744, (32, 17954): 331.3025131083751, (32, 17959): 335.02952715210387, (32, 17963): 334.65824412696753, (32, 18000): 319.6199378738487, (32, 18001): 319.68275704134, (32, 18111): 349.034396965856, (32, 18148): 267.7233579164563, (32, 18166): 297.308801733553, (32, 18189): 328.47333193332196, (32, 18239): 336.87719991901815, (32, 18240): 336.99384504431475, (32, 18245): 337.0911065799577, (32, 18247): 336.89775439577267, (32, 18251): 337.24965711999306, (32, 18256): 337.7885438049554, (32, 18258): 337.4799779475518, (32, 18259): 337.62251140811344, (32, 18260): 337.87459233808414, (32, 18262): 338.2541594066537, (32, 18263): 337.96698027355256, (32, 18264): 338.20897215713404, (32, 18266): 338.48936333898905, (32, 18267): 338.70720714223137, (32, 18268): 338.8649544092563, (32, 18269): 339.313645678315, (32, 18275): 339.1025607103594, (32, 18285): 338.07333797052166, (32, 18308): 333.3696233142502, (32, 18313): 332.15527618606154, (32, 18314): 333.1292467279825, (32, 18315): 338.916068887872, (32, 18316): 339.06471081797065, (32, 18317): 339.2859693870512, (32, 18320): 339.2316428832069, (32, 18321): 339.43506769969775, (32, 18322): 339.7467974192961, (32, 18324): 339.7422310213087, (32, 18325): 340.45998162832336, (32, 18326): 340.1842357614677, (32, 18327): 339.6404106231897, (32, 18329): 340.58038738691846, (32, 18330): 340.7848099498729, (32, 18331): 340.2153566664213, (32, 18332): 339.7224597298913, (32, 18333): 340.54876380172976, (32, 18336): 339.87511046932906, (32, 18337): 340.00347534058983, (32, 18403): 340.65930646396635, (32, 18432): 336.2720007071018, (32, 18451): 339.2557452356954, (32, 18466): 341.73603808892636, (32, 18481): 338.6225075757448, (32, 18483): 338.7506428841035, (32, 18484): 338.2570637288706, (32, 18485): 336.64008305014977, (32, 18486): 337.2401380423568, (32, 18487): 336.16388211412806, (32, 18489): 337.5673182671006, (32, 18490): 338.1347667998705, (32, 18491): 338.56735697532434, (32, 18492): 335.34774217109685, (32, 18493): 336.9320690969785, (32, 18494): 337.4961706513975, (32, 18495): 337.7930460419406, (32, 18496): 337.4456986373513, (32, 18497): 335.7962358092526, (32, 18498): 336.5346234406715, (32, 18499): 337.25711972503285, (32, 18501): 336.5052202715037, (32, 18502): 336.0279755918999, (32, 18503): 335.8197801833459, (32, 18504): 337.78433677660956, (32, 18506): 336.201669032508, (32, 18507): 335.6727217806196, (32, 18508): 337.0307413230468, (32, 18509): 336.91699946620855, (32, 18510): 335.6501571417344, (32, 18511): 336.8069809806389, (32, 18512): 336.50841826260864, (32, 18515): 337.6440141948055, (32, 18516): 337.2542570798143, (32, 18517): 336.46591495596306, (32, 18518): 337.7483177425758, (32, 18519): 337.95859588020596, (32, 18520): 337.0495078163659, (32, 18522): 340.15673265263837, (32, 18523): 340.1118404201234, (32, 18532): 340.5335239348687, (32, 18535): 339.51209652667825, (32, 18537): 338.943669638426, (32, 18539): 338.98826973145293, (32, 18540): 338.97595620996475, (32, 18541): 339.191021226032, (32, 18542): 339.34116015286213, (32, 18543): 338.53757048920124, (32, 18546): 338.67776386132783, (32, 18555): 339.55658856590134, (32, 18556): 339.6198648684921, (32, 18565): 340.27615249609516, (32, 18567): 340.2544092933391, (32, 18568): 339.8940120271265, (32, 18577): 343.399461436301, (32, 18583): 343.2001305383716, (32, 18605): 344.40560512893893, (32, 18608): 339.9875156677972, (32, 18616): 347.6530956531773, (32, 18618): 350.1766646772494, (32, 18625): 350.25820016220246, (32, 18645): 348.23100890345523, (32, 18646): 348.5285292378875, (32, 18653): 345.2202680049474, (32, 18654): 347.4134146325364, (32, 18655): 345.7588220850442, (32, 18666): 356.53007005676733, (32, 18837): 362.40267275995274, (32, 18974): 342.60442560850913, (32, 18999): 346.7535719281494, (32, 19000): 347.6257537124824, (32, 19174): 318.3128025253182, (32, 19342): 338.76996929647885, (32, 19455): 316.05558852884906, (32, 19555): 282.42445271791127, (32, 19564): 290.865958980704, (32, 19573): 287.8741532952348, (32, 19586): 286.1382210442313, (32, 19605): 285.7842272436137, (32, 19611): 287.5725951100157, (32, 19614): 285.09235898298766, (32, 19641): 307.70960128732156, (32, 19702): 309.1548161538934, (32, 19713): 307.1121889011964, (32, 19731): 266.95872193946093, (32, 19819): 313.15391137503497, (32, 19893): 194.634792217005, (32, 19899): 201.89811102411895, (32, 19929): 197.35548365079367, (32, 19951): 215.04162425137062, (32, 19962): 197.13584442767083, (32, 19970): 204.26322401111136, (32, 19971): 203.56825499125367, (32, 19972): 201.54112476466335, (32, 19975): 201.39645611995633, (32, 19978): 222.01582199995224, (32, 19987): 222.8107746634594, (32, 19989): 217.8747798000945, (32, 20039): 223.96275864038302, (32, 20043): 226.71820341974964, (32, 20047): 225.7345535490011, (32, 20052): 219.73442402405047, (32, 20054): 219.82462616548673, (32, 20085): 249.42548615782133, (32, 20104): 251.16721187935016, (32, 20132): 239.86975895956124, (32, 20203): 186.8606194240865, (32, 20280): 182.790320302197, (32, 20285): 181.4580719834142, (32, 20290): 184.0771068858421, (32, 20297): 182.45837887057823, (32, 20309): 218.6227876255373, (32, 20453): 250.50325856142473, (32, 20485): 172.38525893506213, (32, 20520): 168.6911426688907, (32, 20526): 164.68356815861088, (32, 20698): 315.25099832135675, (32, 20868): 350.123472709162, (32, 21042): 179.59322737152795, (32, 21057): 191.04727556226663, (32, 21066): 183.56883303725996, (32, 21075): 184.07494287060462, (32, 21093): 177.85844520629803, (32, 21098): 182.37580995525005, (32, 21127): 179.1444102358866, (32, 21130): 180.032611292787, (32, 21144): 182.13293340807266, (32, 21146): 178.4183434063949, (32, 21147): 182.67532600713537, (32, 21148): 183.78132834286143, (32, 21153): 188.88277472261578, (32, 21293): 195.383772110756, (32, 21426): 215.57768063274125, (32, 21442): 231.59109875327627, (32, 21451): 233.03064634643175, (32, 21466): 222.28714587446768, (32, 21469): 223.51764036399578, (32, 21471): 221.7186133711211, (32, 21473): 222.44534271847158, (32, 21475): 221.47872993629704, (32, 21482): 225.24085160976207, (32, 21484): 224.48698558994883, (32, 21488): 224.02006534690994, (32, 21494): 220.1528503751096, (32, 21498): 221.40676652203612, (32, 21500): 218.38427417827035, (32, 21514): 216.67666194727033, (32, 21537): 215.13839784914734, (32, 21662): 214.75750171830074, (32, 21691): 208.56884443816816, (32, 21757): 208.12457769057679, (32, 21777): 150.18235726632741, (32, 21778): 148.73974827553909, (32, 21779): 148.24304799542588, (32, 21790): 153.2211204142281, (32, 21802): 150.61987568509338, (32, 21824): 150.89668142899018, (32, 21874): 147.03538169630022, (32, 21879): 143.81053783198286, (32, 21983): 163.02309923383953, (32, 22002): 171.20808022061365, (32, 22132): 190.25713237654668, (32, 22261): 155.99242425918624, (32, 22298): 150.81376269104607, (32, 22339): 171.26041733570318, (32, 22508): 119.39127991330831, (32, 22841): 659.4654001825216, (32, 22842): 659.2260197933325, (32, 22874): 653.6167209740283, (32, 22941): 654.9527636629679, (32, 22956): 657.6417128382606, (32, 22960): 659.0959924908165, (32, 22968): 658.5499172673798, (32, 22970): 659.8393139101584, (32, 22974): 659.120270629445, (32, 22980): 662.5885039691957, (32, 23025): 659.1350136308945, (32, 23028): 657.7172439466166, (32, 23081): 659.7107489315123, (32, 23104): 648.1353362686906, (32, 23147): 626.3437884187902, (32, 23298): 238.9749329792376, (32, 23376): 233.63888997001206, (32, 23381): 225.50246651281358, (32, 23529): 238.44020483130396, (32, 23556): 235.93330091822125, (32, 23718): 239.8543957879483, (32, 24001): 271.99142316279904, (32, 24094): 274.7068533410861, (32, 24129): 280.22920423198724, (32, 24174): 265.9093082658343, (32, 24235): 276.38476694308173, (32, 24259): 283.49573767045285, (32, 24260): 282.8232009031234, (32, 24261): 281.89192159813007, (32, 24305): 290.5858930720156, (32, 24306): 291.297788130568, (32, 24307): 289.8892307322048, (32, 24308): 290.5414599536464, (32, 24498): 309.976300425406, (32, 24499): 309.96772583681866, (32, 24500): 309.08618314361416, (32, 24668): 309.296064850749, (32, 24711): 313.9910956120208, (32, 24756): 315.4719194133703, (32, 24788): 317.98662355526506, (32, 24809): 309.6277358406821, (32, 24813): 312.41746435725923, (32, 24821): 311.58321887781347, (32, 24825): 311.8457055065372, (32, 24832): 309.34525628959085, (32, 24833): 310.4157253860963, (32, 24835): 311.37466154705373, (32, 24837): 313.3293739257578, (32, 24840): 309.0501677302358, (32, 24841): 310.9720376499333, (32, 24844): 308.92402700068635, (32, 24845): 310.58342196149107, (32, 24846): 309.5290112524379, (32, 24849): 310.02910503599793, (32, 24850): 312.53041708093593, (32, 24863): 298.92701208907715, (32, 24866): 300.90464635257956, (32, 24885): 302.57904231015846, (32, 24886): 302.36142297951153, (32, 24889): 307.93688084805814, (32, 24903): 310.1680432756288, (32, 24909): 304.1284798487092, (32, 24999): 391.2026319903144, (32, 25019): 390.38891729389155, (32, 25028): 389.7614570619565, (32, 25137): 180.48751614625957, (32, 25145): 182.78801032671993, (32, 25208): 206.08399652171263, (32, 25233): 202.93447078372643, (32, 25371): 183.77649153340195, (32, 25377): 178.42034419693843, (32, 25828): 69.98714846242541, (32, 25851): 62.51321649859322, (32, 25874): 73.1044371625628, (32, 25898): 74.3947237269915, (32, 25946): 68.7823806286253, (32, 26047): 95.8521650678307, (32, 26066): 151.03906525527123, (32, 26197): 117.32673433011696, (32, 26212): 24.0, (32, 26253): 24.0, (32, 26254): 24.0, (32, 26257): 24.0, (32, 26258): 24.0, (32, 26260): 24.0, (32, 26266): 24.0, (32, 26267): 24.0, (32, 26271): 24.0, (32, 26304): 26.3170741337529, (32, 26305): 27.241224099510628, (32, 26363): 59.23795534356853, (32, 26441): 149.75708806596023, (32, 26442): 149.26511056818498, (32, 26450): 145.96136978126123, (32, 26459): 144.98395154138768, (32, 26462): 145.15091545835693, (32, 26467): 154.73758710744508, (32, 26471): 152.38190656984267, (32, 26472): 152.19802165777853, (32, 26473): 152.1865390062343, (32, 26476): 151.76099533316614, (32, 26485): 146.9577744006172, (32, 26493): 147.43596011765598, (32, 26524): 146.30735028864078, (32, 26525): 146.1020907454026, (32, 26556): 151.05369187754312, (32, 26560): 150.1992388253476, (32, 26561): 148.00752980813857, (32, 26564): 150.32537130771018, (32, 26569): 147.6719617862036, (32, 26570): 147.05007016269178, (32, 26573): 147.87677078217504, (32, 26581): 148.08255945599976, (32, 26583): 147.19152098082063, (32, 26593): 148.47819083390138, (32, 26837): 155.65536002206622, (32, 26844): 157.72038445420446, (32, 26863): 153.93963133313713, (32, 26893): 160.12542226359096, (32, 26902): 162.9353212981374, (32, 26905): 159.47092314466235, (32, 26912): 161.8641210991193, (32, 26921): 156.85659320126032, (32, 26922): 152.41710241807203, (32, 27212): 170.09949242816987, (32, 27218): 167.9864374109343, (32, 27239): 174.188086046074, (32, 27257): 171.83961623569013, (32, 27274): 174.94513787669015, (32, 27279): 174.29691186984857, (32, 27282): 171.8365671249803, (32, 27283): 173.16591783851737, (32, 27285): 175.95070299007668, (32, 27286): 173.39053696159905, (32, 27290): 169.70423018132172, (32, 27295): 168.4665596162195, (32, 27300): 175.44171710262177, (32, 27344): 168.0644678006166, (32, 27366): 170.7012803878773, (32, 27383): 175.80440106494794, (32, 27398): 179.22785973183915, (32, 27406): 176.9136975976319, (32, 27407): 177.7884723732444, (32, 27426): 175.98977512773348, (32, 27432): 164.95214499403545, (32, 27460): 172.0797084799875, (32, 27523): 169.87435848495514, (32, 27545): 215.6060357420191, (32, 27602): 271.0763015053271, (32, 27606): 272.199082360854, (32, 27646): 212.3466870196825, (32, 27667): 223.63223445754878, (32, 27672): 224.2342457136941, (32, 27674): 222.30386903270696, (32, 27688): 223.97524130133084, (32, 27692): 226.17525823070625, (32, 27693): 224.4838281992964, (32, 27705): 224.38800236950217, (32, 27712): 225.21635951273137, (32, 27786): 277.1704716758706, (32, 27790): 272.86076944731695, (32, 27791): 272.6487327829516, (32, 27795): 273.91308360738833, (32, 27801): 270.4722712037995, (32, 27813): 278.68665236529716, (32, 27816): 277.00346174880843, (32, 27823): 270.3637607626747, (32, 27830): 274.97057683338863, (32, 27884): 193.5154071426905, (32, 27885): 207.58866622355623, (32, 27896): 199.0523046973465, (32, 27919): 198.46378398043746, (32, 27922): 200.2209659402181, (32, 27930): 195.62577656667293, (32, 27934): 196.17215267426465, (32, 27935): 196.58135204334005, (32, 27948): 265.32552255748334, (32, 27951): 267.8294454370506, (32, 28061): 238.93578161903716, (32, 28290): 343.96285510325947, (32, 28292): 347.1158164266291, (32, 28293): 344.6417563884857, (32, 28295): 344.20570338776645, (32, 28296): 344.12741817092785, (32, 28297): 342.3527549282092, (32, 28302): 342.0040981837979, (32, 28310): 445.14336639344964, (32, 28313): 448.8845062414861, (32, 28372): 445.3432143589235, (32, 28398): 445.80915029380856, (32, 28399): 445.3238585117884, (32, 28400): 446.6118209237228, (32, 28401): 442.748664077322, (32, 28445): 448.97124196921317, (32, 28475): 437.4743656938712, (32, 28885): 265.01299064740147, (32, 28886): 263.4999857245111, (32, 28915): 262.5085145615902, (32, 28916): 262.2292086939475, (32, 28917): 261.25582778496056, (32, 28921): 267.36198210591493, (32, 28931): 266.57550446746995, (32, 28945): 255.1025638764576, (32, 28982): 258.4340492566029, (32, 29219): 254.78438285814474, (32, 29228): 250.51973367681651, (32, 29246): 274.40723371372917, (32, 29248): 272.5079443665606, (32, 29282): 267.04239159465317, (32, 29290): 278.8175433975428, (32, 29291): 277.23408263794994, (32, 29292): 278.49778378889374, (32, 29293): 276.29625244552005, (32, 29294): 277.40208003549753, (32, 29298): 276.05777317889164, (32, 29299): 275.4599068777441, (32, 29304): 274.3154157046044, (32, 29317): 269.6275381648115, (32, 29323): 269.3145057267169, (32, 29330): 271.48907181221443, (32, 29331): 272.92697825245796, (32, 29344): 251.8579133792376, (32, 29445): 195.33238802787997, (32, 29724): 660.5293114970526, (32, 29738): 661.4331415762758, (32, 29745): 659.1375190778136, (32, 29748): 661.3905703243684, (32, 29750): 663.5982637338846, (32, 29759): 659.9387507373723, (32, 29772): 663.3070285766706, (32, 29781): 662.6213723989316, (32, 29784): 661.3012747394513, (32, 29790): 663.6600181989082, (32, 29811): 662.5127512455117, (32, 29817): 673.2744726113532, (32, 29818): 672.6377142376422, (32, 29929): 657.7436429917241, (32, 30039): 664.7730276807027, (32, 30066): 654.397508739879, (32, 30116): 627.2997106149775, (32, 30238): 587.1949124391664, (32, 30248): 601.8361914656173, (32, 30260): 601.8463165737553, (32, 30545): 256.51062944016275, (32, 30733): 217.1872305539124, (32, 30756): 193.40407424038708, (32, 30921): 218.9205557492253, (32, 31079): 216.86072397035096, (32, 31149): 198.81289896694307, (32, 31154): 201.33465826253936, (32, 31160): 198.27831316012256, (32, 31163): 200.88545486800547, (32, 31189): 184.63358416246632, (32, 31215): 187.8812749125091, (32, 31259): 197.90193350486547, (32, 31262): 195.67932193475724, (32, 31430): 225.39483378107863, (32, 31568): 215.52933677181207, (32, 31751): 215.52579234514016, (38, 109): 301.64457522403507, (38, 872): 755.523469827924, (38, 873): 757.9619869642688, (38, 877): 757.0304864814176, (38, 879): 757.3905650268908, (38, 884): 754.9024070106437, (38, 889): 756.4387731585546, (38, 891): 754.1002839560608, (38, 892): 759.2842740113439, (38, 894): 758.9833451799344, (38, 896): 756.6611959788847, (38, 903): 757.1025879351633, (38, 909): 753.0050855846252, (38, 910): 753.9966391503664, (38, 912): 752.3798832613428, (38, 913): 750.5930030787209, (38, 916): 749.858168295902, (38, 926): 754.8160282895589, (38, 927): 754.0001596329939, (38, 948): 753.219247451139, (38, 961): 754.6939535918885, (38, 962): 754.9812923009658, (38, 963): 755.300799027723, (38, 967): 758.1404657552208, (38, 974): 756.7914623971826, (38, 998): 759.0910378257311, (38, 1014): 812.5814796019164, (38, 1086): 749.801146531073, (38, 1087): 749.4988214183909, (38, 1089): 747.2369249470731, (38, 1090): 748.2687337362323, (38, 1092): 751.798217708751, (38, 1097): 749.1048344433015, (38, 1107): 753.5588408312688, (38, 1387): 379.82631793006664, (38, 1554): 341.5700911735012, (38, 1827): 866.0064699439484, (38, 1828): 866.2856194304064, (38, 1829): 866.6443094833469, (38, 1830): 866.1594480017892, (38, 1831): 866.3954015321326, (38, 1832): 866.1434216136109, (38, 1833): 866.1899526187952, (38, 1836): 865.9289348087414, (38, 1841): 867.4615561727181, (38, 1843): 866.8089038913071, (38, 1844): 867.0823995809301, (38, 1845): 866.2903146927968, (38, 1847): 863.825124549523, (38, 1848): 864.6852096136014, (38, 1849): 868.6985432983234, (38, 1850): 869.1365814039088, (38, 1851): 865.2978025839485, (38, 1852): 865.3211083869858, (38, 1854): 865.7644317747337, (38, 1856): 863.650764254783, (38, 1857): 864.6049927062026, (38, 1858): 868.3343206316299, (38, 1861): 866.556196356877, (38, 1866): 863.5615987831678, (38, 1867): 867.5398628359367, (38, 1868): 867.0478950092071, (38, 1870): 866.9591589118912, (38, 1871): 867.4544675728614, (38, 1875): 865.7475305612126, (38, 1880): 864.2253607375354, (38, 1882): 864.4235940329488, (38, 1883): 869.2151414196426, (38, 1889): 864.7413118235166, (38, 1893): 866.7546954466346, (38, 1894): 866.1537290964246, (38, 1899): 864.2282334664002, (38, 1900): 864.6922174805295, (38, 1902): 867.8162762252356, (38, 1905): 868.5801303823383, (38, 1907): 865.3126784082018, (38, 1910): 865.6514345486733, (38, 1917): 870.3662374788457, (38, 1920): 865.4059384993625, (38, 1935): 868.7618572257484, (38, 1937): 869.421870819394, (38, 1946): 862.9537674023642, (38, 1949): 863.7265345597071, (38, 1950): 860.9851725756045, (38, 1951): 862.2876872938364, (38, 1952): 863.147349115313, (38, 1953): 863.6524932560466, (38, 1954): 862.9850621348174, (38, 1958): 863.4724912933117, (38, 1960): 864.7299590491949, (38, 1968): 865.2263436294271, (38, 1969): 868.988563407595, (38, 1974): 867.998475335086, (38, 1975): 867.9648094411215, (38, 1979): 866.1874835922529, (38, 1980): 865.9752645078078, (38, 1981): 866.5516537770517, (38, 1985): 867.009721690895, (38, 1994): 859.791674056515, (38, 2011): 864.3665148585911, (38, 2019): 870.6221027527334, (38, 2020): 869.7945392005647, (38, 2029): 866.5802801557292, (38, 2030): 869.2220519151393, (38, 2032): 866.017454212122, (38, 2033): 867.7613327974937, (38, 2034): 867.6952996886652, (38, 2036): 864.3402928446286, (38, 2037): 865.2052802077247, (38, 2038): 865.6532151652183, (38, 2042): 875.3109363886762, (38, 2050): 867.3789756770324, (38, 2051): 867.2006652326462, (38, 2053): 867.4741817489529, (38, 2054): 868.3274623376705, (38, 2066): 866.5841577622933, (38, 2067): 866.6095972994493, (38, 2071): 858.1970893062303, (38, 2072): 859.8286839619443, (38, 2073): 855.5142524031696, (38, 2074): 855.2746214286943, (38, 2080): 852.5065350347211, (38, 2082): 860.7004443366193, (38, 2083): 861.5463006735127, (38, 2089): 859.8077842894554, (38, 2090): 860.6026336705287, (38, 2092): 859.563682590018, (38, 2098): 853.5884122695278, (38, 2099): 854.5048193451871, (38, 2101): 853.3903213246122, (38, 2102): 857.8150187650281, (38, 2103): 856.4120092457941, (38, 2104): 855.6309480446371, (38, 2106): 862.0943057874887, (38, 2112): 853.9516491279281, (38, 2113): 858.427097472591, (38, 2114): 859.4433285998865, (38, 2117): 862.7318523585332, (38, 2123): 857.2161520522623, (38, 2124): 858.12823707258, (38, 2134): 855.4861456251189, (38, 2138): 858.1873705322555, (38, 2141): 855.8157080858695, (38, 2148): 856.9671300792197, (38, 2150): 853.5876999540236, (38, 2151): 854.5351528710266, (38, 2152): 853.0717581799873, (38, 2153): 857.2937762821008, (38, 2154): 853.5266996455022, (38, 2155): 853.0585013767662, (38, 2156): 852.3791124448835, (38, 2157): 853.2122888671971, (38, 2160): 859.3790243964407, (38, 2161): 852.8972629688102, (38, 2162): 857.3767911001033, (38, 2163): 856.1023027805513, (38, 2164): 856.0040108827403, (38, 2168): 853.8659216030688, (38, 2172): 854.6304753393082, (38, 2174): 854.4030924906173, (38, 2178): 855.3521807593485, (38, 2179): 854.754565846734, (38, 2183): 858.1056755728198, (38, 2185): 858.152667664675, (38, 2186): 857.4301691672804, (38, 2190): 859.5771902097653, (38, 2192): 858.2727963311444, (38, 2193): 858.3671791641954, (38, 2194): 857.0344634480207, (38, 2195): 856.8194775112012, (38, 2197): 858.5471210097581, (38, 2205): 856.6495420905788, (38, 2207): 854.1869750855282, (38, 2208): 855.5595973968369, (38, 2212): 858.8037378307434, (38, 2214): 831.4743888932095, (38, 2225): 834.5895310959728, (38, 2231): 828.8063442998867, (38, 2278): 847.6440372504404, (38, 2284): 850.3269325687794, (38, 2285): 849.9194484121565, (38, 2291): 844.3099394642613, (38, 2292): 845.1036390565275, (38, 2307): 848.5402409244122, (38, 2313): 843.600760347535, (38, 2317): 843.1556777089442, (38, 2319): 846.0275356324379, (38, 2321): 847.2533656759413, (38, 2323): 847.1432214069534, (38, 2326): 852.038127542059, (38, 2327): 850.8515540918147, (38, 2329): 850.0360921530607, (38, 2330): 849.0943562727236, (38, 2332): 851.0234232660438, (38, 2344): 848.0753206399461, (38, 2346): 847.9825366328079, (38, 2361): 847.817577863448, (38, 2368): 861.4953936129313, (38, 2374): 862.7729048398867, (38, 2375): 863.2283525860771, (38, 2377): 858.6962460487879, (38, 2378): 864.0349022064407, (38, 2379): 864.1117346481892, (38, 2380): 864.5888850317509, (38, 2383): 859.9346101035867, (38, 2385): 860.6511560510716, (38, 2395): 860.7614836113542, (38, 2397): 863.5525460085623, (38, 2398): 857.2481801666712, (38, 2399): 858.904575499511, (38, 2400): 858.537682288727, (38, 2402): 861.0352390059406, (38, 2403): 862.0506438501224, (38, 2404): 862.3281334931145, (38, 2405): 859.8667123929168, (38, 2407): 861.8947824321066, (38, 2408): 863.070108330019, (38, 2409): 860.6193879550223, (38, 2411): 861.977340794303, (38, 2412): 861.7358397001566, (38, 2413): 862.5596833290572, (38, 2414): 861.1964482942001, (38, 2422): 861.6447561609579, (38, 2424): 862.0369579464879, (38, 2426): 862.2703651897319, (38, 2433): 860.351278523612, (38, 2436): 859.8039285564307, (38, 2437): 853.8849720184483, (38, 2440): 855.2013383092916, (38, 2445): 881.0211077788117, (38, 2447): 877.8455318098031, (38, 2454): 880.8804217483097, (38, 2455): 881.0888975932551, (38, 2460): 871.6114880221963, (38, 2461): 872.7726200072096, (38, 2471): 891.344898276486, (38, 2492): 869.4289219851984, (38, 2511): 860.3779427557093, (38, 2523): 865.0015464517444, (38, 2525): 863.4573560552425, (38, 2535): 867.0550843908708, (38, 2537): 864.9367476563278, (38, 2538): 866.4521039356242, (38, 2539): 865.5737166761279, (38, 2540): 868.009312963599, (38, 2542): 869.4495966979974, (38, 2559): 899.7425937045687, (38, 2575): 896.7363472192994, (38, 2599): 852.4006859336421, (38, 2600): 862.3267470989557, (38, 2607): 856.7756697122622, (38, 2627): 865.0960012531159, (38, 2647): 870.3864179015794, (38, 2674): 867.9080254170996, (38, 2681): 866.97047430998, (38, 2683): 869.7391817940965, (38, 2686): 866.731429278234, (38, 2689): 902.4781990071915, (38, 2690): 902.6102753550857, (38, 2713): 908.2492042046989, (38, 2714): 908.6709270066095, (38, 2715): 909.5629310217025, (38, 2739): 908.8254562563212, (38, 2740): 903.6993669424718, (38, 2741): 904.1779174425454, (38, 2749): 907.4015813312033, (38, 2750): 907.7452744999266, (38, 2752): 908.4106279069211, (38, 2755): 909.0748219597209, (38, 2758): 908.8144281368895, (38, 2759): 908.8466975079448, (38, 2769): 907.8848460896082, (38, 2771): 905.009963023056, (38, 2779): 904.823510216503, (38, 2784): 894.5909058290392, (38, 2800): 895.9147566149912, (38, 2802): 901.7298109207449, (38, 2803): 901.4481061499945, (38, 2804): 900.875436416619, (38, 2805): 902.3065650431332, (38, 2807): 902.3093208512316, (38, 2809): 901.8473084383711, (38, 2812): 896.2789032134957, (38, 2814): 901.1554163430995, (38, 2817): 900.8125475525454, (38, 2819): 902.5676412592293, (38, 2823): 896.3264422648957, (38, 2832): 903.330451770676, (38, 2836): 899.3275687658494, (38, 2839): 902.3554993515917, (38, 2841): 901.2853578041841, (38, 2843): 901.0841209249954, (38, 2846): 899.8798578815051, (38, 2849): 903.8558058822117, (38, 2852): 902.9844398825999, (38, 2853): 904.2532172754517, (38, 2876): 904.3811984859834, (38, 2877): 907.5508895236982, (38, 2885): 907.9452791199194, (38, 2918): 903.3863408297575, (38, 2921): 904.7006012974635, (38, 2925): 898.7033351758613, (38, 2926): 896.7934932762433, (38, 2930): 900.8068142545073, (38, 2931): 899.1511406340909, (38, 2938): 903.306355081109, (38, 2940): 907.7714240291748, (38, 2947): 903.1724887565202, (38, 2949): 900.9863615195634, (38, 2950): 901.5118683408084, (38, 2952): 900.8275615752304, (38, 2958): 900.7339891060727, (38, 2959): 901.5008556196617, (38, 2960): 902.9822248099546, (38, 2961): 902.2098801243325, (38, 2963): 900.1013902985279, (38, 2968): 900.478201478329, (38, 2976): 899.9779496602312, (38, 2981): 886.3093638075402, (38, 2982): 885.8184273564544, (38, 2984): 885.1159036459296, (38, 3003): 883.7991960019452, (38, 3046): 876.2413985958782, (38, 3050): 882.5956869604255, (38, 3051): 883.1729603846327, (38, 3053): 881.6345730217898, (38, 3069): 889.7816542562991, (38, 3071): 881.5294153765775, (38, 3080): 907.7565578542749, (38, 3199): 880.8688480044407, (38, 3200): 879.2107329332392, (38, 3205): 889.0017751112293, (38, 3209): 880.0214241976096, (38, 3215): 879.3737138917029, (38, 3217): 877.413627803247, (38, 3249): 879.6205037642752, (38, 3263): 894.4493167160083, (38, 3289): 884.4775421614654, (38, 3301): 884.7813546894386, (38, 3302): 884.1366932609309, (38, 3307): 883.2743971602462, (38, 3310): 885.6248998740084, (38, 3391): 883.9633934495133, (38, 3509): 573.4484204687271, (38, 3510): 572.0641806314487, (38, 3511): 573.0687127295886, (38, 3512): 572.2845295879457, (38, 3514): 572.640513420088, (38, 3519): 576.2881954197065, (38, 3536): 576.0357144477086, (38, 3545): 578.2909453742118, (38, 3548): 576.27465420874, (38, 3572): 576.7219501045192, (38, 3581): 574.7683868121693, (38, 3583): 574.1666305222662, (38, 3601): 578.7584140973997, (38, 3656): 576.1878324222076, (38, 3669): 572.7719230876343, (38, 3670): 573.9830809395856, (38, 3695): 567.1888063606965, (38, 3696): 568.1820675276081, (38, 3782): 578.1387240911954, (38, 3792): 576.4154586805302, (38, 3989): 30.011538105910642, (38, 4008): 36.91434143502307, (38, 4031): 40.053655080399054, (38, 4045): 34.13711514315428, (38, 4144): 31.373223473221227, (38, 4145): 24.0, (38, 4164): 27.804789326480158, (38, 4168): 24.060235597113014, (38, 4173): 24.0, (38, 4181): 24.0, (38, 4228): 24.0, (38, 4248): 24.0, (38, 4254): 43.01056046900862, (38, 4260): 41.22680247941326, (38, 4262): 39.772742435257, (38, 4273): 39.247604117761156, (38, 4319): 72.05928827625547, (38, 4326): 72.48966594739093, (38, 4328): 71.70695484565377, (38, 4334): 71.49198320597273, (38, 4335): 72.39948701477664, (38, 4372): 300.8324831187399, (38, 4413): 314.0548646071958, (38, 4434): 298.86920027870696, (38, 4447): 294.4987587155051, (38, 4452): 299.7734496350215, (38, 4463): 323.6507486298204, (38, 4465): 321.84836480367613, (38, 4619): 331.36438346622845, (38, 4645): 329.09122403392433, (38, 4657): 331.1052978757008, (38, 4666): 332.8341362405109, (38, 4676): 332.98457614691284, (38, 4678): 332.0490019506512, (38, 4689): 334.3766485025497, (38, 4704): 335.94506552337975, (38, 4726): 386.3834818124068, (38, 4727): 385.612157427567, (38, 4730): 383.98463794513765, (38, 4731): 385.33664085700786, (38, 4734): 381.1108077618569, (38, 4735): 381.14482366550504, (38, 4736): 382.1760177468083, (38, 4737): 381.78461343104357, (38, 4738): 382.4926652091013, (38, 4756): 383.66810208620143, (38, 4760): 376.08215526916604, (38, 4761): 375.01108890097476, (38, 4762): 375.9505228039993, (38, 4765): 376.9080233376625, (38, 4773): 387.16568175448737, (38, 4774): 387.69618599994516, (38, 4790): 386.4694669416394, (38, 4795): 385.48956933960534, (38, 4799): 388.6750804194544, (38, 4801): 391.9570232519492, (38, 4804): 384.2236669808627, (38, 4805): 383.43616534763987, (38, 4806): 389.1996941706464, (38, 4815): 389.5330632452614, (38, 4816): 390.90899905117135, (38, 4817): 392.6900436055945, (38, 4826): 391.1102534543583, (38, 4830): 390.6148466682415, (38, 4839): 378.38147581750576, (38, 4840): 379.6725901518179, (38, 4841): 378.5521395132019, (38, 4846): 377.78317173557076, (38, 4848): 378.8319839650116, (38, 4850): 379.7338766623299, (38, 4871): 365.32478916712296, (38, 4883): 373.4395356747359, (38, 4900): 367.5281317986651, (38, 4901): 367.56949339309807, (38, 4917): 355.2755534154555, (38, 4931): 352.0974943308354, (38, 4944): 354.7350711345156, (38, 4956): 353.5777016304066, (38, 4958): 355.2749460782476, (38, 4959): 355.90444308068874, (38, 4961): 353.4858036064126, (38, 4966): 353.8485348371902, (38, 5207): 350.63717219342976, (38, 5272): 256.9588569452681, (38, 5283): 257.65276355762757, (38, 5287): 262.9561689564223, (38, 5289): 263.4486987799919, (38, 5293): 253.05710630635585, (38, 5295): 254.44097227346126, (38, 5296): 256.9602282239613, (38, 5298): 258.35357360570225, (38, 5303): 260.98122671074407, (38, 5305): 261.5502556388395, (38, 5306): 264.72825095814403, (38, 5307): 261.5126292594209, (38, 5308): 262.5982247908009, (38, 5313): 259.406366938102, (38, 5314): 258.77060947106895, (38, 5317): 264.2435167048917, (38, 5319): 261.05396469347414, (38, 5324): 258.8142836377453, (38, 5326): 257.23382888075474, (38, 5348): 266.7746783113899, (38, 5351): 270.6654649975715, (38, 5399): 267.48362911300194, (38, 5413): 276.9320883165867, (38, 5422): 265.27368860416624, (38, 5445): 265.13808646221366, (38, 5448): 264.6905146442008, (38, 5456): 267.25945533042466, (38, 5467): 268.39026713212667, (38, 5624): 256.3917985477109, (38, 5671): 238.13535708810076, (38, 5672): 236.67000421827126, (38, 5797): 256.5661374646082, (38, 5871): 301.10169687883774, (38, 5976): 293.94657910783326, (38, 6118): 735.090121668995, (38, 6248): 762.7906940737408, (38, 6345): 257.98569881498213, (38, 6352): 264.5090136955575, (38, 6354): 256.4132898056109, (38, 6359): 255.10006851840072, (38, 6376): 263.4646828890933, (38, 6378): 257.1793945075371, (38, 6381): 255.6144299259506, (38, 6383): 259.37586126598063, (38, 6396): 256.32674544389795, (38, 6399): 257.8784912927268, (38, 6408): 264.2864153106291, (38, 6409): 261.3088491243608, (38, 6419): 271.92250370337854, (38, 6422): 263.48491211685746, (38, 6423): 264.0133053629635, (38, 6424): 257.1694925559064, (38, 6439): 258.44855195584216, (38, 6464): 260.27465127903906, (38, 6465): 260.87337444201194, (38, 6469): 259.9897272439149, (38, 6470): 260.3725273959011, (38, 6472): 252.88726171586558, (38, 6480): 254.41302328020356, (38, 6486): 250.9588859205422, (38, 6497): 252.10681660392106, (38, 6503): 260.2007688357638, (38, 6508): 259.5396052590333, (38, 6509): 258.3967526764597, (38, 6521): 253.72905108889503, (38, 6544): 254.36588908017885, (38, 6552): 262.58603985210226, (38, 6553): 263.5990279406204, (38, 6554): 264.6276527339877, (38, 6578): 260.87058785947426, (38, 6582): 261.8005043394231, (38, 6601): 260.44147521829046, (38, 6609): 252.16809879927257, (38, 6610): 251.90713357033255, (38, 6611): 251.64262514162795, (38, 6614): 252.14093259236893, (38, 6615): 251.97019332350663, (38, 6616): 250.9953171712165, (38, 6617): 251.42597389367302, (38, 6618): 250.0394089409079, (38, 6619): 252.88732731513088, (38, 6620): 251.0236195222017, (38, 6621): 251.8945510804208, (38, 6622): 251.65742043761065, (38, 6623): 252.26712570022855, (38, 6624): 253.07480084070875, (38, 6625): 253.21584223792087, (38, 6626): 252.92382938441247, (38, 6627): 252.33275791365884, (38, 6628): 251.25992025747215, (38, 6629): 252.89079999406266, (38, 6630): 253.9093686187944, (38, 6632): 252.95268133468193, (38, 6634): 254.86084313709924, (38, 6635): 252.17581850249616, (38, 6636): 250.96344876485603, (38, 6637): 254.07884423530552, (38, 6638): 253.83066823475102, (38, 6639): 252.256664553506, (38, 6640): 253.67008474905356, (38, 6641): 251.96097875885175, (38, 6642): 253.83316085342526, (38, 6643): 253.0055234225661, (38, 6645): 252.78006042515224, (38, 6646): 250.3058867291591, (38, 6647): 253.55991876961193, (38, 6653): 252.0000614111401, (38, 6655): 252.2390224413723, (38, 6658): 254.93660527384142, (38, 6662): 253.91053311789358, (38, 6819): 303.852718064269, (38, 6996): 289.13100437185267, (38, 7059): 277.78379634468905, (38, 7187): 305.92924835215024, (38, 7304): 323.91014853237914, (38, 7528): 293.15045825755266, (38, 7720): 224.02498799502757, (38, 7793): 227.0070805827129, (38, 7807): 225.5533873403305, (38, 7808): 227.7416191300624, (38, 7831): 246.36188039071232, (38, 7850): 235.0247775589206, (38, 7852): 237.45709607242702, (38, 8012): 225.31143893320453, (38, 8125): 230.64875113523522, (38, 8208): 204.185420263538, (38, 8392): 240.4649845422313, (38, 8651): 359.41804850624715, (38, 9088): 307.52221173391086, (38, 9443): 393.5613731042735, (38, 9444): 392.16712018613606, (38, 9828): 448.6331239295369, (38, 9868): 444.7006596084171, (38, 10180): 231.1157078944237, (38, 10256): 208.0356888117922, (38, 10276): 215.61367728936372, (38, 10378): 204.2592780736081, (38, 10676): 253.73608132281572, (38, 10714): 273.3895021602465, (38, 10730): 259.7632032303729, (38, 10862): 415.3842911834778, (38, 10881): 414.35116105572405, (38, 10883): 415.1661194839408, (38, 10885): 415.43562752957206, (38, 10891): 416.44985983868395, (38, 10909): 414.86850759205475, (38, 10911): 413.0078983528353, (38, 10913): 413.8004901415372, (38, 10915): 412.92727759273157, (38, 10919): 412.0399805849276, (38, 11037): 440.29936064957275, (38, 11039): 436.1240095757489, (38, 11516): 136.44550517237462, (38, 11856): 71.03684067233816, (38, 11857): 74.33169252286991, (38, 11861): 72.70936730008314, (38, 11881): 70.34851058351943, (38, 11902): 73.94677270641266, (38, 11911): 72.4442067907071, (38, 11914): 72.85554506343598, (38, 11922): 70.90197242317119, (38, 11924): 69.46002450850757, (38, 11926): 70.364899783622, (38, 11950): 65.79559589093112, (38, 11963): 62.78400032440423, (38, 11983): 61.07084301777699, (38, 11985): 61.58758284195747, (38, 12009): 58.57401953304237, (38, 12010): 61.63424712606282, (38, 12018): 60.80826955974597, (38, 12020): 60.68612004672931, (38, 12021): 59.940760762414584, (38, 12024): 57.86441000224879, (38, 12025): 59.28226542882682, (38, 12027): 59.58537507390602, (38, 12031): 62.03610598786077, (38, 12032): 61.81647427438203, (38, 12035): 57.92747231206858, (38, 12041): 63.600666017930195, (38, 12045): 94.60955642153803, (38, 12145): 74.53298163766529, (38, 12275): 40.988550031295134, (38, 12294): 43.8650660901213, (38, 12358): 59.68956216660834, (38, 12463): 70.49795767654012, (38, 12465): 70.55769119612448, (38, 12482): 69.93422567108291, (38, 12503): 70.3689737949538, (38, 12506): 71.1306241220348, (38, 12549): 65.4110701914276, (38, 12559): 65.60441726144074, (38, 12569): 67.68347064230109, (38, 12572): 68.18105236474793, (38, 12574): 66.69517969594686, (38, 12576): 65.64907895463182, (38, 12591): 63.355879817721316, (38, 12608): 67.44951315672071, (38, 12696): 57.35681713828265, (38, 12710): 60.22859735398586, (38, 12728): 60.10472296331935, (38, 12766): 163.4707947768313, (38, 12771): 168.7570197067645, (38, 12790): 170.06958048532042, (38, 12795): 173.4757713888843, (38, 12797): 183.26210134114032, (38, 12798): 181.57938312485416, (38, 12811): 172.53269736296187, (38, 12830): 176.06573241728844, (38, 12848): 173.48173959334477, (38, 12850): 172.1590380625337, (38, 12852): 176.1847801212525, (38, 12854): 177.579582431204, (38, 12859): 171.8383234428332, (38, 12861): 179.8184552079695, (38, 12865): 171.29555905696364, (38, 12866): 171.6927581660221, (38, 12867): 169.20198943125692, (38, 12874): 170.45125657675632, (38, 12875): 169.26490891995087, (38, 12881): 173.93456862117492, (38, 12883): 172.18258749687297, (38, 12885): 168.4279834456345, (38, 12888): 172.76868247519883, (38, 12889): 172.9552913108085, (38, 12892): 170.27814823748645, (38, 12893): 172.9230877679812, (38, 12896): 171.87394133355727, (38, 12906): 171.3815238009495, (38, 13018): 190.87198370310477, (38, 13071): 192.64472342775707, (38, 13131): 196.96108714211988, (38, 13146): 186.65699510060557, (38, 13159): 207.29886162628236, (38, 13193): 198.37128259817445, (38, 13198): 212.94097013056867, (38, 13292): 193.5135654230601, (38, 13296): 186.54924224690805, (38, 13406): 226.11261000731398, (38, 13407): 226.91171454430952, (38, 13417): 230.40781676487333, (38, 13418): 229.06462302701786, (38, 13438): 220.06392823195145, (38, 13442): 217.8898338986581, (38, 13443): 219.36233436192975, (38, 13764): 357.4437488711956, (38, 13766): 355.6181863589683, (38, 13771): 358.43243462762075, (38, 13783): 357.30335010120467, (38, 13784): 353.1874087111182, (38, 13792): 363.53998698557825, (38, 13824): 358.75417766721085, (38, 14017): 342.6719193020877, (38, 14870): 380.0746605381267, (38, 14997): 314.92369656855504, (38, 15000): 315.0562829442634, (38, 15003): 314.20042633261977, (38, 15006): 310.2285804183703, (38, 15007): 309.06876728594483, (38, 15056): 310.13347304012734, (38, 15063): 311.3770993822229, (38, 15069): 312.1404171925486, (38, 15076): 309.08962439681585, (38, 15086): 312.4550374334088, (38, 15087): 314.1397189027643, (38, 15111): 317.4325648383065, (38, 15116): 315.56807065809954, (38, 15722): 347.06244654417037, (38, 15998): 376.5578439158429, (38, 16073): 622.5105556725514, (38, 16939): 787.4227216574865, (38, 16940): 785.6459946072109, (38, 16951): 787.5027946137731, (38, 16963): 787.714787680737, (38, 16965): 789.9499049349059, (38, 16969): 789.3203580568492, (38, 16970): 788.5562076925476, (38, 16971): 786.5484309766849, (38, 16973): 786.3539371691037, (38, 16974): 790.791211460752, (38, 16976): 788.7493826169203, (38, 16978): 787.30333356923, (38, 16980): 789.5415305496641, (38, 16982): 790.713048694066, (38, 17045): 846.0800039440904, (38, 17048): 848.6313681422729, (38, 17304): 24.0, (38, 17305): 24.0, (38, 17330): 24.0, (38, 17334): 24.0, (38, 17343): 24.0, (38, 17345): 24.0, (38, 17347): 24.0, (38, 17351): 24.0, (38, 17372): 24.0, (38, 17373): 24.0, (38, 17377): 24.0, (38, 17382): 24.0, (38, 17383): 24.0, (38, 17389): 24.0, (38, 17400): 24.0, (38, 17401): 24.0, (38, 17402): 24.0, (38, 17403): 24.0, (38, 17440): 24.0, (38, 17455): 24.0, (38, 17491): 24.0, (38, 17507): 24.0, (38, 17509): 24.0, (38, 17590): 24.0, (38, 17615): 29.633855017399455, (38, 17642): 27.074662160615585, (38, 17643): 26.045044675263167, (38, 17668): 30.397663634848723, (38, 17721): 39.449695018076376, (38, 17754): 34.9093336499366, (38, 17769): 24.0, (38, 17776): 24.0, (38, 17804): 24.0, (38, 17809): 24.0, (38, 17824): 24.0, (38, 17837): 24.0, (38, 17838): 24.0, (38, 17862): 24.0, (38, 17866): 24.0, (38, 17872): 24.0, (38, 17873): 24.0, (38, 17881): 24.0, (38, 17947): 641.9433091471996, (38, 17951): 638.5073489564805, (38, 17953): 637.8522345248318, (38, 17954): 638.093429045286, (38, 17959): 641.2349733365552, (38, 17963): 640.0204379798855, (38, 18000): 622.5398538216334, (38, 18001): 623.2328961134137, (38, 18111): 671.9022010924608, (38, 18148): 584.4287767085268, (38, 18166): 618.3016121291562, (38, 18189): 649.8566818200862, (38, 18239): 24.0, (38, 18240): 24.0, (38, 18245): 24.0, (38, 18247): 24.0, (38, 18251): 24.0, (38, 18256): 24.0, (38, 18258): 24.0, (38, 18259): 24.0, (38, 18260): 24.0, (38, 18262): 24.0, (38, 18263): 24.0, (38, 18264): 24.0, (38, 18266): 24.0, (38, 18267): 24.0, (38, 18268): 24.0, (38, 18269): 24.0, (38, 18275): 24.0, (38, 18285): 24.0, (38, 18308): 24.0, (38, 18313): 24.0, (38, 18314): 24.0, (38, 18315): 24.0, (38, 18316): 24.0, (38, 18317): 24.0, (38, 18320): 24.0, (38, 18321): 24.0, (38, 18322): 24.0, (38, 18324): 24.0, (38, 18325): 24.0, (38, 18326): 24.0, (38, 18327): 24.0, (38, 18329): 24.0, (38, 18330): 24.0, (38, 18331): 24.0, (38, 18332): 24.0, (38, 18333): 24.0, (38, 18336): 24.0, (38, 18337): 24.0, (38, 18403): 24.0, (38, 18432): 24.0, (38, 18451): 24.0, (38, 18466): 24.0, (38, 18481): 24.0, (38, 18483): 24.0, (38, 18484): 24.0, (38, 18485): 24.0, (38, 18486): 24.0, (38, 18487): 24.0, (38, 18489): 24.0, (38, 18490): 24.0, (38, 18491): 24.0, (38, 18492): 24.0, (38, 18493): 24.0, (38, 18494): 24.0, (38, 18495): 24.0, (38, 18496): 24.0, (38, 18497): 24.0, (38, 18498): 24.0, (38, 18499): 24.0, (38, 18501): 24.0, (38, 18502): 24.0, (38, 18503): 24.0, (38, 18504): 24.0, (38, 18506): 24.0, (38, 18507): 24.0, (38, 18508): 24.0, (38, 18509): 24.0, (38, 18510): 24.0, (38, 18511): 24.0, (38, 18512): 24.0, (38, 18515): 24.0, (38, 18516): 24.0, (38, 18517): 24.0, (38, 18518): 24.0, (38, 18519): 24.0, (38, 18520): 24.0, (38, 18522): 24.0, (38, 18523): 24.0, (38, 18532): 24.0, (38, 18535): 24.0, (38, 18537): 24.0, (38, 18539): 24.0, (38, 18540): 24.0, (38, 18541): 24.0, (38, 18542): 24.0, (38, 18543): 24.0, (38, 18546): 24.0, (38, 18555): 24.0, (38, 18556): 24.0, (38, 18565): 24.0, (38, 18567): 24.0, (38, 18568): 24.0, (38, 18577): 24.0, (38, 18583): 24.0, (38, 18605): 24.0, (38, 18608): 24.0, (38, 18616): 24.0, (38, 18618): 24.0, (38, 18625): 24.0, (38, 18645): 24.0, (38, 18646): 24.0, (38, 18653): 24.0, (38, 18654): 24.0, (38, 18655): 24.0, (38, 18666): 24.0, (38, 18837): 49.25766953757673, (38, 18974): 24.0, (38, 18999): 24.0, (38, 19000): 24.0, (38, 19174): 70.64325261777955, (38, 19342): 65.8119888162203, (38, 19455): 51.029974668816905, (38, 19555): 100.62442468905694, (38, 19564): 103.876498811503, (38, 19573): 104.34441603299047, (38, 19586): 104.20419779787417, (38, 19605): 102.59930856377353, (38, 19611): 101.9843485515237, (38, 19614): 100.70971142606659, (38, 19641): 84.63170286001963, (38, 19702): 87.23155661571147, (38, 19713): 87.74745358305776, (38, 19731): 101.71042854425836, (38, 19819): 61.66337638728951, (38, 19893): 163.8918103153632, (38, 19899): 167.51501403755302, (38, 19929): 162.5310605858172, (38, 19951): 163.06748187141798, (38, 19962): 166.59739659378073, (38, 19970): 157.88259967041105, (38, 19971): 159.86106174638033, (38, 19972): 161.3733527040117, (38, 19975): 160.0344565703546, (38, 19978): 154.0092005375141, (38, 19987): 152.62200184258626, (38, 19989): 152.207319339325, (38, 20039): 152.0369604818555, (38, 20043): 150.32704474460547, (38, 20047): 148.3814582763256, (38, 20052): 149.5272447279421, (38, 20054): 150.46224578539739, (38, 20085): 141.57708152998723, (38, 20104): 141.61489952817843, (38, 20132): 143.87166041488558, (38, 20203): 181.96649785575394, (38, 20280): 188.00538612873945, (38, 20285): 190.5163154233863, (38, 20290): 186.7799221042446, (38, 20297): 186.49979676166924, (38, 20309): 169.2745146492165, (38, 20453): 160.64125728518948, (38, 20485): 186.1375496688166, (38, 20520): 185.92578974384074, (38, 20526): 191.9696289263214, (38, 20698): 427.37911832391825, (38, 20868): 492.5622491059537, (38, 21042): 170.93468004122158, (38, 21057): 157.63622179712414, (38, 21066): 164.70187518131414, (38, 21075): 166.42827489629667, (38, 21093): 170.7123193861971, (38, 21098): 162.61018090548598, (38, 21127): 170.24211908583823, (38, 21130): 168.1312941934757, (38, 21144): 167.76856708833168, (38, 21146): 171.1060570784036, (38, 21147): 167.78692983103633, (38, 21148): 165.72323192772458, (38, 21153): 169.18584203689394, (38, 21293): 149.98641729711508, (38, 21426): 150.29119501609398, (38, 21442): 137.28239241677184, (38, 21451): 136.04962735786472, (38, 21466): 143.56807574873366, (38, 21469): 141.48708455698159, (38, 21471): 144.62958154753707, (38, 21473): 142.8771960633767, (38, 21475): 144.40902325838778, (38, 21482): 140.28454428576964, (38, 21484): 140.6570722856118, (38, 21488): 141.909417489684, (38, 21494): 144.29177185960262, (38, 21498): 142.7741545074018, (38, 21500): 145.09767188344264, (38, 21514): 140.8555672576982, (38, 21537): 145.41986236512798, (38, 21662): 139.20673348695738, (38, 21691): 147.26424879709623, (38, 21757): 161.63943754869, (38, 21777): 199.1925719454786, (38, 21778): 201.16947973724086, (38, 21779): 200.55769800933444, (38, 21790): 196.4488326053387, (38, 21802): 197.50903869114666, (38, 21824): 195.9798775524951, (38, 21874): 200.6788287811865, (38, 21879): 202.83121044049767, (38, 21983): 189.72379229601043, (38, 22002): 171.6030401115638, (38, 22132): 178.25259275655498, (38, 22261): 472.4453851221698, (38, 22298): 468.8498403462061, (38, 22339): 494.4137591204081, (38, 22508): 432.05830823255525, (38, 22841): 865.7030369153707, (38, 22842): 865.8601627104321, (38, 22874): 861.4326590798869, (38, 22941): 861.4385168188904, (38, 22956): 864.5765959026245, (38, 22960): 865.1117438451722, (38, 22968): 870.0576521896131, (38, 22970): 870.6048974390702, (38, 22974): 873.2975922192408, (38, 22980): 876.9305980402197, (38, 23025): 878.2405117479791, (38, 23028): 877.7671732954115, (38, 23081): 885.8523231959441, (38, 23104): 881.8717778822754, (38, 23147): 845.3847862375592, (38, 23298): 106.23153646845607, (38, 23376): 112.1312033318002, (38, 23381): 117.11436761069808, (38, 23529): 103.59181994534357, (38, 23556): 106.79128521486685, (38, 23718): 109.25534991360742, (38, 24001): 71.21002076250622, (38, 24094): 63.07699026724292, (38, 24129): 57.314623854037904, (38, 24174): 71.33831432770731, (38, 24235): 60.6627894608155, (38, 24259): 53.49733691865582, (38, 24260): 54.17586725687083, (38, 24261): 55.099356974016224, (38, 24305): 46.41580231715295, (38, 24306): 45.74530377661217, (38, 24307): 47.11574242672088, (38, 24308): 57.42495113575698, (38, 24498): 27.7254417400359, (38, 24499): 27.662406256830618, (38, 24500): 28.666850391282956, (38, 24668): 36.64104209955084, (38, 24711): 24.0, (38, 24756): 24.0, (38, 24788): 24.0, (38, 24809): 29.48255905850303, (38, 24813): 26.33182121402778, (38, 24821): 27.212619092500812, (38, 24825): 27.231527013920132, (38, 24832): 29.561335026897154, (38, 24833): 28.56872525228632, (38, 24835): 27.791780954563926, (38, 24837): 25.74632805200513, (38, 24840): 29.956435031332113, (38, 24841): 27.92157522896854, (38, 24844): 30.241472996267177, (38, 24845): 28.062253895549127, (38, 24846): 29.969545729732275, (38, 24849): 29.605163010464743, (38, 24850): 26.433458697718578, (38, 24863): 38.603149388655225, (38, 24866): 36.63357515898425, (38, 24885): 35.30334884858418, (38, 24886): 35.74971464394645, (38, 24889): 29.550901899242387, (38, 24903): 27.10064006558136, (38, 24909): 32.89100689735594, (38, 24999): 55.13867989159229, (38, 25019): 55.07380326266922, (38, 25028): 53.57399991610644, (38, 25137): 212.20966070906877, (38, 25145): 210.9945346031516, (38, 25208): 222.59195826806697, (38, 25233): 224.51888818459352, (38, 25371): 197.26244421079622, (38, 25377): 196.4123252764363, (38, 25828): 267.8048976668038, (38, 25851): 275.26158948639153, (38, 25874): 264.0026758121029, (38, 25898): 264.7420628498277, (38, 25946): 268.7726335715986, (38, 26047): 256.2246196310311, (38, 26066): 192.66109287864995, (38, 26197): 227.94595138218827, (38, 26212): 332.671194672409, (38, 26253): 339.175624844605, (38, 26254): 336.2731549132304, (38, 26257): 335.3610643385411, (38, 26258): 338.2627569063216, (38, 26260): 336.6681403378254, (38, 26266): 336.07539025688635, (38, 26267): 334.6520057290936, (38, 26271): 334.9644062629854, (38, 26304): 310.7269540583466, (38, 26305): 309.9474768860975, (38, 26363): 280.06616506751413, (38, 26441): 484.67314280089465, (38, 26442): 484.0466511298313, (38, 26450): 480.76847357695755, (38, 26459): 480.3279245897494, (38, 26462): 480.7046876312357, (38, 26467): 490.29243578537603, (38, 26471): 487.69748194234444, (38, 26472): 487.43988955043073, (38, 26473): 487.355746016183, (38, 26476): 486.0923101249698, (38, 26485): 482.0470242595858, (38, 26493): 482.2416882716271, (38, 26524): 482.0608263600279, (38, 26525): 481.7351026474636, (38, 26556): 486.39211221440274, (38, 26560): 485.9217113014728, (38, 26561): 483.81339631780475, (38, 26564): 485.5494142919247, (38, 26569): 483.3598748825659, (38, 26570): 482.59424107285315, (38, 26573): 483.2073634074406, (38, 26581): 483.2111455134922, (38, 26583): 482.4460012764622, (38, 26593): 483.3349068790316, (38, 26837): 491.0229278676195, (38, 26844): 493.17575733377834, (38, 26863): 488.6840581610926, (38, 26893): 494.9589510034571, (38, 26902): 497.88925881713647, (38, 26905): 494.7489581135764, (38, 26912): 497.0917762778244, (38, 26921): 491.67771542493216, (38, 26922): 486.0874127822282, (38, 27212): 501.4255533646803, (38, 27218): 498.5716872844893, (38, 27239): 505.6804947731988, (38, 27257): 503.5623201187559, (38, 27274): 506.5761359895657, (38, 27279): 506.1853929913643, (38, 27282): 503.70191423393925, (38, 27283): 504.53045397574357, (38, 27285): 507.747454234695, (38, 27286): 505.60733589579536, (38, 27290): 501.5919264211189, (38, 27295): 499.94474061478525, (38, 27300): 506.9736720314768, (38, 27344): 500.67740138643836, (38, 27366): 503.56393300834867, (38, 27383): 508.126719809238, (38, 27398): 510.96740929683756, (38, 27406): 508.4405247323705, (38, 27407): 509.11158448319196, (38, 27426): 505.3187452316668, (38, 27432): 494.7370098710544, (38, 27460): 501.2909319851372, (38, 27523): 505.5819732631997, (38, 27545): 548.2786252247854, (38, 27602): 605.330506171311, (38, 27606): 606.2752591907206, (38, 27646): 548.5598043974622, (38, 27667): 559.9100241189981, (38, 27672): 560.4501048466757, (38, 27674): 558.5495598267776, (38, 27688): 559.9518261094676, (38, 27692): 562.4762168358861, (38, 27693): 560.7886743722205, (38, 27705): 560.7618603940205, (38, 27712): 561.6440943283046, (38, 27786): 605.1620245388507, (38, 27790): 597.6696478784679, (38, 27791): 596.968705762233, (38, 27795): 602.0575217026695, (38, 27801): 596.5824911734213, (38, 27813): 607.0364503614594, (38, 27816): 604.7506732533907, (38, 27823): 596.3647163501626, (38, 27830): 601.9902133605394, (38, 27884): 530.2821079787687, (38, 27885): 543.8938395787972, (38, 27896): 535.6320704915166, (38, 27919): 535.0035710450217, (38, 27922): 536.7886279098309, (38, 27930): 532.2729062859552, (38, 27934): 532.8489382116477, (38, 27935): 533.2962879995019, (38, 27948): 602.3020600828994, (38, 27951): 604.6034518225916, (38, 28061): 552.017403479003, (38, 28290): 670.1941521544929, (38, 28292): 672.4986034892138, (38, 28293): 670.6341729185549, (38, 28295): 669.5388733278921, (38, 28296): 670.0314406980203, (38, 28297): 668.9590698063975, (38, 28302): 668.0350549043127, (38, 28310): 695.4160472329385, (38, 28313): 696.62682090382, (38, 28372): 698.1632181573463, (38, 28398): 698.2654096106071, (38, 28399): 697.4081245630781, (38, 28400): 698.6427532670906, (38, 28401): 695.5521824452313, (38, 28445): 695.095616814339, (38, 28475): 693.8947439002792, (38, 28885): 76.48497081157912, (38, 28886): 78.08383170708359, (38, 28915): 80.56663506147116, (38, 28916): 80.21289559763925, (38, 28917): 81.33978193395279, (38, 28921): 74.2767937078703, (38, 28931): 75.3351729141625, (38, 28945): 90.2221806855301, (38, 28982): 85.58607416702463, (38, 29219): 100.88962538773582, (38, 29228): 102.61805632688014, (38, 29246): 106.73416699845879, (38, 29248): 111.0437983315744, (38, 29282): 110.03210121057525, (38, 29290): 102.43976917204243, (38, 29291): 103.56617717378275, (38, 29292): 103.12817318686312, (38, 29293): 102.85472063904747, (38, 29294): 104.89020627101017, (38, 29298): 104.00368403119509, (38, 29299): 105.1314601428649, (38, 29304): 102.40730895246232, (38, 29317): 100.74416314888519, (38, 29323): 100.5090490985623, (38, 29330): 101.42782096869722, (38, 29331): 100.98067541179843, (38, 29344): 108.54676899814682, (38, 29445): 149.15993655815765, (38, 29724): 849.989952009454, (38, 29738): 850.9715494927185, (38, 29745): 847.8167743313406, (38, 29748): 846.8985906457934, (38, 29750): 847.8744263058271, (38, 29759): 845.7356852276101, (38, 29772): 849.3391602064606, (38, 29781): 848.5096620240923, (38, 29784): 848.5299536220588, (38, 29790): 849.0320700602537, (38, 29811): 846.3186804342491, (38, 29817): 849.045643985585, (38, 29818): 848.2110595401376, (38, 29929): 848.3924150391194, (38, 30039): 865.1915876756526, (38, 30066): 859.1929897142337, (38, 30116): 822.7917988228768, (38, 30238): 769.0338964121656, (38, 30248): 799.5735350541948, (38, 30260): 800.5249688892214, (38, 30545): 80.56931739005238, (38, 30733): 125.58047661320987, (38, 30756): 145.68302035429528, (38, 30921): 119.14832791726559, (38, 31079): 258.6192374123247, (38, 31149): 259.0896593895839, (38, 31154): 259.8430296411594, (38, 31160): 259.3438452422351, (38, 31163): 260.5824730332369, (38, 31189): 278.7051074112054, (38, 31215): 278.29102102817285, (38, 31259): 284.3815130663035, (38, 31262): 286.0857124900456, (38, 31430): 260.2136927149418, (38, 31568): 319.6258234437129, (38, 31751): 270.9533288714948, (41, 109): 167.01275561568534, (41, 872): 650.3431000521889, (41, 873): 652.8673116018756, (41, 877): 652.4713399257719, (41, 879): 652.8993751822419, (41, 884): 651.5970772422039, (41, 889): 652.9161793987929, (41, 891): 650.6148715699509, (41, 892): 654.7422274377803, (41, 894): 654.1980114305601, (41, 896): 650.8500894970344, (41, 903): 653.1951646201635, (41, 909): 647.0901545249595, (41, 910): 647.5878534299457, (41, 912): 646.040233813223, (41, 913): 644.5243792321277, (41, 916): 643.1330781317332, (41, 926): 647.7417372957506, (41, 927): 646.7801000178127, (41, 948): 649.6121202408063, (41, 961): 648.8499249967407, (41, 962): 648.7789046985192, (41, 963): 648.8143098463376, (41, 967): 654.0384653105767, (41, 974): 653.969588394613, (41, 998): 655.4897495722945, (41, 1014): 704.2940401529111, (41, 1086): 629.0967702294553, (41, 1087): 626.9048535837006, (41, 1089): 625.5770454709683, (41, 1090): 626.7864880498261, (41, 1092): 630.401889541383, (41, 1097): 628.014107825346, (41, 1107): 631.0167266390566, (41, 1387): 278.47384979763206, (41, 1554): 262.2081502022529, (41, 1827): 777.4782726804461, (41, 1828): 777.5146607194632, (41, 1829): 778.0659456990562, (41, 1830): 778.7628331447023, (41, 1831): 778.7957368717355, (41, 1832): 778.4145520380131, (41, 1833): 778.2564429398632, (41, 1836): 777.7493488428651, (41, 1841): 779.6634097211631, (41, 1843): 778.977785871688, (41, 1844): 779.4703452354194, (41, 1845): 778.8187340367824, (41, 1847): 775.6225599192878, (41, 1848): 776.6005037941994, (41, 1849): 781.370398624224, (41, 1850): 781.676288274724, (41, 1851): 777.8511001622792, (41, 1852): 778.3564171105979, (41, 1854): 778.4804937726802, (41, 1856): 776.0608227650479, (41, 1857): 776.7718274152409, (41, 1858): 780.6233688352535, (41, 1861): 778.3803829542107, (41, 1866): 776.3754712232187, (41, 1867): 779.3429942271681, (41, 1868): 778.4357989602177, (41, 1870): 779.9556629767022, (41, 1871): 778.8514492290232, (41, 1875): 778.1373629603071, (41, 1880): 776.2759545671141, (41, 1882): 777.1827660014402, (41, 1883): 781.2180734757634, (41, 1889): 776.0456652974848, (41, 1893): 777.4032687144319, (41, 1894): 776.6226149318675, (41, 1899): 775.1679875979, (41, 1900): 775.5020522265479, (41, 1902): 778.5414080307256, (41, 1905): 779.6732856000932, (41, 1907): 776.7933576580072, (41, 1910): 776.5655950509453, (41, 1917): 780.0267957453822, (41, 1920): 776.4718402521476, (41, 1935): 778.9485001719046, (41, 1937): 779.8127375329288, (41, 1946): 772.7221656079483, (41, 1949): 773.2896431231916, (41, 1950): 771.6199495240307, (41, 1951): 772.6673217422498, (41, 1952): 774.8000818677776, (41, 1953): 774.1882316478863, (41, 1954): 774.325223844821, (41, 1958): 773.5390740045084, (41, 1960): 775.159880880882, (41, 1968): 775.7967957527712, (41, 1969): 778.2620408187131, (41, 1974): 777.694039489617, (41, 1975): 777.9694960164875, (41, 1979): 775.543693765434, (41, 1980): 776.2532214246058, (41, 1981): 776.2587154670042, (41, 1985): 776.4684462590795, (41, 1994): 772.521828898683, (41, 2011): 777.4399779929967, (41, 2019): 785.1843157670885, (41, 2020): 784.1669488970865, (41, 2029): 781.1311371831129, (41, 2030): 783.4484161035246, (41, 2032): 781.0624316001966, (41, 2033): 782.2568112590328, (41, 2034): 782.6458152002751, (41, 2036): 781.1999884722167, (41, 2037): 781.5035123546115, (41, 2038): 779.818207481641, (41, 2042): 790.2097838353343, (41, 2050): 781.1802974817624, (41, 2051): 781.4818194935131, (41, 2053): 781.5593717968209, (41, 2054): 782.4939694749667, (41, 2066): 780.6715601410806, (41, 2067): 780.4463429268253, (41, 2071): 770.5700953640852, (41, 2072): 771.9280697309308, (41, 2073): 766.1190442605262, (41, 2074): 766.1792289992162, (41, 2080): 764.057831208053, (41, 2082): 772.7621971198736, (41, 2083): 773.4372039736934, (41, 2089): 771.2796893197577, (41, 2090): 771.831996999255, (41, 2092): 770.4812682588246, (41, 2098): 764.5595721216426, (41, 2099): 765.8004184442653, (41, 2101): 764.7826805688859, (41, 2102): 768.8029394945609, (41, 2103): 767.7010957460835, (41, 2104): 767.287458930884, (41, 2106): 774.1950511589476, (41, 2112): 765.6896933161656, (41, 2113): 769.6217701875458, (41, 2114): 771.2839507294619, (41, 2117): 775.1548817513095, (41, 2123): 753.0243648218626, (41, 2124): 753.8506901576214, (41, 2134): 752.5899455506471, (41, 2138): 754.5840964455075, (41, 2141): 752.5399962917694, (41, 2148): 757.9743309551685, (41, 2150): 750.7319854556126, (41, 2151): 751.9124273356903, (41, 2152): 750.5638330164535, (41, 2153): 757.8520336395715, (41, 2154): 754.1603596934073, (41, 2155): 754.4782032974194, (41, 2156): 753.3308996879176, (41, 2157): 756.7950095497418, (41, 2160): 757.7794403062206, (41, 2161): 750.8416256299314, (41, 2162): 759.5924754785444, (41, 2163): 758.2880620693152, (41, 2164): 758.4657471694587, (41, 2168): 753.2371097657038, (41, 2172): 755.9443364370339, (41, 2174): 752.3453408739698, (41, 2178): 757.1900625820963, (41, 2179): 756.8140737541222, (41, 2183): 755.018088327677, (41, 2185): 755.3321050096837, (41, 2186): 754.5331326930049, (41, 2190): 757.4792636639831, (41, 2192): 756.1309754153872, (41, 2193): 755.1034059872792, (41, 2194): 753.7281299904326, (41, 2195): 754.0912280150845, (41, 2197): 756.7005153577749, (41, 2205): 755.5686507659376, (41, 2207): 753.9196913692723, (41, 2208): 754.9535608088569, (41, 2212): 754.2720018618418, (41, 2214): 736.6421589566398, (41, 2225): 741.3500388067924, (41, 2231): 723.2631394407736, (41, 2278): 757.9979429442789, (41, 2284): 761.611024871573, (41, 2285): 761.5924108700736, (41, 2291): 758.5938303331659, (41, 2292): 756.2841748878453, (41, 2307): 759.9126608951705, (41, 2313): 758.8567672242098, (41, 2317): 753.0963655810976, (41, 2319): 757.508049713957, (41, 2321): 759.2397717393648, (41, 2323): 758.2579475640051, (41, 2326): 761.514780365992, (41, 2327): 760.327627673541, (41, 2329): 759.6018990052756, (41, 2330): 758.968286823302, (41, 2332): 761.3072488114303, (41, 2344): 757.1036574203976, (41, 2346): 757.6200399385901, (41, 2361): 752.3668054087607, (41, 2368): 768.9869822309525, (41, 2374): 770.7393452913408, (41, 2375): 770.8930419144567, (41, 2377): 765.8801872334294, (41, 2378): 771.966665295625, (41, 2379): 772.6568450660812, (41, 2380): 772.7051187332652, (41, 2383): 766.7585738976145, (41, 2385): 767.269353769257, (41, 2395): 766.8378641487006, (41, 2397): 772.3669776552972, (41, 2398): 764.3470916314767, (41, 2399): 765.7484966811284, (41, 2400): 765.3625093386235, (41, 2402): 769.6166458304947, (41, 2403): 770.6950251587157, (41, 2404): 770.7381679854872, (41, 2405): 768.3505389479405, (41, 2407): 769.9551997823053, (41, 2408): 771.4640388335691, (41, 2409): 768.9851556945115, (41, 2411): 771.6383909067334, (41, 2412): 770.9990095676682, (41, 2413): 772.0139187718445, (41, 2414): 770.7055646883844, (41, 2422): 771.6417611137239, (41, 2424): 771.0945766864969, (41, 2426): 771.1344227627153, (41, 2433): 769.5058263506224, (41, 2436): 769.596969584714, (41, 2437): 763.1694749905655, (41, 2440): 764.4158153286614, (41, 2445): 797.123768687937, (41, 2447): 793.200189498432, (41, 2454): 796.3769221060022, (41, 2455): 796.1060625638688, (41, 2460): 786.8411750570581, (41, 2461): 788.0822012759354, (41, 2471): 810.1825812732269, (41, 2492): 806.4844623424899, (41, 2511): 793.9976489186873, (41, 2523): 800.4471554261871, (41, 2525): 799.8990373300488, (41, 2535): 793.4710759881606, (41, 2537): 791.6166245569293, (41, 2538): 792.4620377249931, (41, 2539): 793.9815978307643, (41, 2540): 794.3671513645672, (41, 2542): 796.4586376131239, (41, 2559): 821.6043009239276, (41, 2575): 821.4840306859376, (41, 2599): 770.6957029259476, (41, 2600): 782.1472367826502, (41, 2607): 773.8557182943774, (41, 2627): 807.3360235957937, (41, 2647): 814.3440632600701, (41, 2674): 809.2231265408994, (41, 2681): 809.5343961122336, (41, 2683): 811.7764517171292, (41, 2686): 808.1097411697488, (41, 2689): 845.6191691648769, (41, 2690): 846.0586005355206, (41, 2713): 860.8864710899767, (41, 2714): 862.5468877559265, (41, 2715): 863.393934124892, (41, 2739): 862.3347126247376, (41, 2740): 854.0673485891358, (41, 2741): 854.2815051129081, (41, 2749): 862.2621183375445, (41, 2750): 862.1578752767352, (41, 2752): 862.5949527882757, (41, 2755): 863.500731142791, (41, 2758): 863.6157226402094, (41, 2759): 863.4523465676442, (41, 2769): 862.0423912465886, (41, 2771): 856.2021457904876, (41, 2779): 859.1747579002424, (41, 2784): 850.7034383044983, (41, 2800): 855.0731293310181, (41, 2802): 853.8623160265548, (41, 2803): 853.1968470743778, (41, 2804): 852.4893632889483, (41, 2805): 855.6082835917967, (41, 2807): 855.2116591987898, (41, 2809): 855.6574403502303, (41, 2812): 849.2786806286717, (41, 2814): 857.6270862470493, (41, 2817): 860.8488918626138, (41, 2819): 854.4828374920432, (41, 2823): 852.7679866825013, (41, 2832): 857.1607952833516, (41, 2836): 853.2405890537816, (41, 2839): 854.8510698510311, (41, 2841): 859.5068174779665, (41, 2843): 858.6737771156485, (41, 2846): 855.3924228809045, (41, 2849): 858.3492576678256, (41, 2852): 857.2403698045547, (41, 2853): 858.8806779030626, (41, 2876): 860.8644519716637, (41, 2877): 864.2433061805539, (41, 2885): 868.4037041659252, (41, 2918): 852.7217533202726, (41, 2921): 854.4914874734233, (41, 2925): 845.0594531921482, (41, 2926): 841.2580755674779, (41, 2930): 851.6057622237942, (41, 2931): 846.6054328931201, (41, 2938): 853.3400275700714, (41, 2940): 854.4540575087409, (41, 2947): 849.0407126560184, (41, 2949): 850.2058724134334, (41, 2950): 851.409690803708, (41, 2952): 850.7540298507032, (41, 2958): 850.3792446876845, (41, 2959): 850.3425186100318, (41, 2960): 852.0717561419784, (41, 2961): 851.6228781262545, (41, 2963): 850.151789393184, (41, 2968): 850.9315093306653, (41, 2976): 849.6135848040167, (41, 2981): 841.1404827860621, (41, 2982): 841.4766260003614, (41, 2984): 840.9827608315481, (41, 3003): 840.6057116274252, (41, 3046): 824.0000433247327, (41, 3050): 834.5627234844062, (41, 3051): 834.8121030496671, (41, 3053): 833.664205443076, (41, 3069): 842.8999959536582, (41, 3071): 831.7034222191139, (41, 3080): 869.5736250368531, (41, 3199): 842.7156019917912, (41, 3200): 841.6797677445477, (41, 3205): 850.546129052066, (41, 3209): 842.542531575379, (41, 3215): 841.3906585197454, (41, 3217): 839.6479389324696, (41, 3249): 841.1471077566288, (41, 3263): 854.1463660199797, (41, 3289): 844.2208445851594, (41, 3301): 845.6366122462335, (41, 3302): 844.641350121127, (41, 3307): 843.7528052674293, (41, 3310): 846.388391332211, (41, 3391): 866.6631494751932, (41, 3509): 545.8799950103788, (41, 3510): 544.6581608416044, (41, 3511): 544.9215823639868, (41, 3512): 543.6834338322111, (41, 3514): 543.5031597577757, (41, 3519): 551.4283480935434, (41, 3536): 547.0684945969854, (41, 3545): 548.4321500914732, (41, 3548): 545.8344553255474, (41, 3572): 548.4314121204598, (41, 3581): 548.7791748628318, (41, 3583): 545.687204286592, (41, 3601): 554.5730996268019, (41, 3656): 554.6684524108399, (41, 3669): 556.7478755890623, (41, 3670): 558.0346000353354, (41, 3695): 549.9039254349505, (41, 3696): 550.6905560964286, (41, 3782): 536.6140572524317, (41, 3792): 536.7570046090387, (41, 3989): 362.3342853227943, (41, 4008): 368.1822790439248, (41, 4031): 372.19002364713253, (41, 4045): 365.9252791462128, (41, 4144): 362.0969508683073, (41, 4145): 351.7061229115961, (41, 4164): 358.7703136755851, (41, 4168): 354.8310692328353, (41, 4173): 353.3987210191264, (41, 4181): 349.8967234559745, (41, 4228): 351.4288028586042, (41, 4248): 343.4962340633684, (41, 4254): 293.2569454965139, (41, 4260): 295.6427873195296, (41, 4262): 295.96822222885686, (41, 4273): 297.0357095275536, (41, 4319): 268.41307554705185, (41, 4326): 268.4178117160389, (41, 4328): 269.28069049414955, (41, 4334): 268.44982766975653, (41, 4335): 267.61919015046465, (41, 4372): 40.74594642050267, (41, 4413): 24.0, (41, 4434): 42.761189870692185, (41, 4447): 44.256035074061444, (41, 4452): 41.91177384501363, (41, 4463): 78.67116433876762, (41, 4465): 77.09371723900597, (41, 4619): 24.0, (41, 4645): 24.0, (41, 4657): 24.0, (41, 4666): 24.0, (41, 4676): 24.0, (41, 4678): 24.0, (41, 4689): 24.0, (41, 4704): 24.0, (41, 4726): 70.39707693757059, (41, 4727): 69.46863860318335, (41, 4730): 67.60104948382656, (41, 4731): 68.58238694350261, (41, 4734): 67.18440565355307, (41, 4735): 66.64939135761503, (41, 4736): 67.39440303823255, (41, 4737): 66.25737155403318, (41, 4738): 66.72012665147547, (41, 4756): 67.84370584830614, (41, 4760): 61.49355180901081, (41, 4761): 61.392768392521305, (41, 4762): 60.62391794558151, (41, 4765): 62.14090971843841, (41, 4773): 71.85826811468728, (41, 4774): 71.6254619865402, (41, 4790): 71.15444546339842, (41, 4795): 70.19926342194152, (41, 4799): 72.3490647346694, (41, 4801): 75.14877420433298, (41, 4804): 69.80705009065828, (41, 4805): 69.03739504526156, (41, 4806): 72.18299424640969, (41, 4815): 71.85481823375122, (41, 4816): 73.88797014567517, (41, 4817): 75.09252945266327, (41, 4826): 73.47686042796745, (41, 4830): 72.48075922795582, (41, 4839): 64.21069803473488, (41, 4840): 65.29289822644228, (41, 4841): 63.55992142423704, (41, 4846): 62.81598690645656, (41, 4848): 63.14363946412979, (41, 4850): 64.07810239987928, (41, 4871): 51.178324296678944, (41, 4883): 59.7445014926235, (41, 4900): 54.72821735536592, (41, 4901): 53.92372069688432, (41, 4917): 25.130981281098002, (41, 4931): 25.297426864750943, (41, 4944): 24.262575660539067, (41, 4956): 26.044497267113773, (41, 4958): 27.830531591638692, (41, 4959): 29.14426483023925, (41, 4961): 25.22699902143221, (41, 4966): 27.22990735370251, (41, 5207): 29.104392148177425, (41, 5272): 149.418143814121, (41, 5283): 146.87418732438917, (41, 5287): 140.6176046757098, (41, 5289): 139.42658452844978, (41, 5293): 151.24324366986986, (41, 5295): 144.45936622861964, (41, 5296): 143.06802558928814, (41, 5298): 142.36472862485687, (41, 5303): 139.18767840837674, (41, 5305): 148.20025028548667, (41, 5306): 148.27800868433044, (41, 5307): 149.35199128893905, (41, 5308): 146.6560550532526, (41, 5313): 148.4294814697833, (41, 5314): 147.40765357426224, (41, 5317): 145.80474911583966, (41, 5319): 141.1967751919662, (41, 5324): 143.60729055263494, (41, 5326): 145.2544524437683, (41, 5348): 147.78341639082868, (41, 5351): 144.33860711021518, (41, 5399): 136.20494258959343, (41, 5413): 138.8566981205965, (41, 5422): 136.14542037578906, (41, 5445): 141.0982818019185, (41, 5448): 143.37643653041928, (41, 5456): 142.5997321907305, (41, 5467): 140.14331629762984, (41, 5624): 169.56945716044086, (41, 5671): 119.55269687003474, (41, 5672): 122.75154041886292, (41, 5797): 84.13654149793591, (41, 5871): 95.63256592189104, (41, 5976): 121.54514787488586, (41, 6118): 735.844999371025, (41, 6248): 775.8132045934484, (41, 6345): 356.4787273729898, (41, 6352): 361.81487723829383, (41, 6354): 354.5012109279341, (41, 6359): 354.6633454187524, (41, 6376): 363.9070342747916, (41, 6378): 355.269500870631, (41, 6381): 355.9393174973206, (41, 6383): 357.1246287264427, (41, 6396): 361.34231788725276, (41, 6399): 357.86999971647765, (41, 6408): 360.4189907807879, (41, 6409): 354.7212567028339, (41, 6419): 358.4768814397298, (41, 6422): 357.216507804075, (41, 6423): 357.472509502504, (41, 6424): 351.4273726764679, (41, 6439): 351.41777218895317, (41, 6464): 351.89794768915823, (41, 6465): 353.52545843590065, (41, 6469): 355.1753440402, (41, 6470): 356.0360076610278, (41, 6472): 353.3470956271678, (41, 6480): 349.1017557238761, (41, 6486): 340.27446223549924, (41, 6497): 342.96399541228953, (41, 6503): 345.1094245343596, (41, 6508): 348.2170147251884, (41, 6509): 345.5972918331166, (41, 6521): 346.0384753668892, (41, 6544): 343.03756996276513, (41, 6552): 350.626882572945, (41, 6553): 351.1093849192091, (41, 6554): 351.6466966290889, (41, 6578): 350.31095484583483, (41, 6582): 347.25888346475404, (41, 6601): 349.34588798291526, (41, 6609): 348.444022701316, (41, 6610): 347.5349680126477, (41, 6611): 349.34810000655654, (41, 6614): 350.801007279487, (41, 6615): 350.02229438104507, (41, 6616): 346.9073491787846, (41, 6617): 348.0581998081907, (41, 6618): 344.6501336073859, (41, 6619): 350.8391421667807, (41, 6620): 345.69407443255085, (41, 6621): 345.9526573450483, (41, 6622): 346.66561245533336, (41, 6623): 349.54944157239447, (41, 6624): 348.74513419043467, (41, 6625): 349.4847154503051, (41, 6626): 351.3891327140163, (41, 6627): 351.9691811149959, (41, 6628): 344.57487361264396, (41, 6629): 347.13490486514144, (41, 6630): 351.8331033313177, (41, 6632): 347.851643704349, (41, 6634): 351.61519406020267, (41, 6635): 346.7823525672004, (41, 6636): 346.46327084912735, (41, 6637): 347.6988684641023, (41, 6638): 350.6352969840333, (41, 6639): 351.219744525905, (41, 6640): 351.15416849752876, (41, 6641): 345.025906529939, (41, 6642): 349.82823503216736, (41, 6643): 352.2968096668515, (41, 6645): 350.2252906402675, (41, 6646): 345.77792653018577, (41, 6647): 350.1175910590383, (41, 6653): 350.4136211047704, (41, 6655): 351.6024009434565, (41, 6658): 351.1868987992166, (41, 6662): 349.0030189897603, (41, 6819): 364.9017251468238, (41, 6996): 336.92776170784106, (41, 7059): 329.96411429096685, (41, 7187): 306.06540633325295, (41, 7304): 343.5424959507612, (41, 7528): 321.51090655129633, (41, 7720): 296.08132546292273, (41, 7793): 289.91145626960025, (41, 7807): 291.6774541653815, (41, 7808): 288.50017945757617, (41, 7831): 336.5523165485595, (41, 7850): 336.8563458328605, (41, 7852): 339.8522103105444, (41, 8012): 307.33363198697555, (41, 8125): 255.3126200728694, (41, 8208): 284.95101951401, (41, 8392): 312.96212395192305, (41, 8651): 400.5815300407549, (41, 9088): 388.87752232731276, (41, 9443): 372.31093713664274, (41, 9444): 370.32780759887925, (41, 9828): 396.815919915425, (41, 9868): 414.0576518071228, (41, 10180): 251.64065773572378, (41, 10256): 233.17817918869122, (41, 10276): 247.01823593406533, (41, 10378): 263.75674965614013, (41, 10676): 231.94093500802862, (41, 10714): 239.00054930084875, (41, 10730): 254.30825452499056, (41, 10862): 191.75771463000544, (41, 10881): 187.5311477552145, (41, 10883): 188.31677109755955, (41, 10885): 192.59114417358884, (41, 10891): 189.54190912368423, (41, 10909): 189.15290126647372, (41, 10911): 187.7954279118526, (41, 10913): 189.0182064794166, (41, 10915): 188.67365920858197, (41, 10919): 187.75883685776978, (41, 11037): 225.46960205901038, (41, 11039): 232.80594115064346, (41, 11516): 466.8698913232621, (41, 11856): 268.5869183224197, (41, 11857): 265.00949515140115, (41, 11861): 266.7352932374113, (41, 11881): 270.6849035434739, (41, 11902): 269.6391159044355, (41, 11911): 272.68467978675557, (41, 11914): 271.4157041803242, (41, 11922): 271.0619117926639, (41, 11924): 272.14641031486866, (41, 11926): 272.02752567479155, (41, 11950): 276.1920658434713, (41, 11963): 276.7776975098734, (41, 11983): 281.8692334294053, (41, 11985): 276.8074312433771, (41, 12009): 281.5260448699007, (41, 12010): 279.85393254353176, (41, 12018): 280.59062624220826, (41, 12020): 280.0169855594917, (41, 12021): 280.6360610186215, (41, 12024): 281.13581587150105, (41, 12025): 279.96503008216985, (41, 12027): 280.0934838239153, (41, 12031): 279.7457544356468, (41, 12032): 279.13320860081944, (41, 12035): 282.61787300958076, (41, 12041): 273.99606610149533, (41, 12045): 275.0270144705447, (41, 12145): 281.18728282719485, (41, 12275): 373.80840679824433, (41, 12294): 376.09687533515745, (41, 12358): 391.0823846717747, (41, 12463): 400.66266325464284, (41, 12465): 400.8467741096828, (41, 12482): 398.0534754512054, (41, 12503): 398.96117823840484, (41, 12506): 399.3512516084185, (41, 12549): 392.98147642425914, (41, 12559): 393.79622021082406, (41, 12569): 396.07207217170446, (41, 12572): 396.24862560067965, (41, 12574): 395.2712425946594, (41, 12576): 392.64424381033876, (41, 12591): 389.380892773936, (41, 12608): 389.2963575386953, (41, 12696): 383.60899056713436, (41, 12710): 381.38698026477573, (41, 12728): 384.95650369519205, (41, 12766): 353.7084052581366, (41, 12771): 342.6534892717403, (41, 12790): 343.1005737621462, (41, 12795): 345.54069379567943, (41, 12797): 339.0132729312039, (41, 12798): 338.5282243835522, (41, 12811): 339.06033014086745, (41, 12830): 340.96763897984505, (41, 12848): 336.7757629906702, (41, 12850): 334.2341292965407, (41, 12852): 339.6645203692515, (41, 12854): 339.6221302525291, (41, 12859): 335.69935930238796, (41, 12861): 337.6015211066293, (41, 12865): 341.030026720126, (41, 12866): 339.73133110591436, (41, 12867): 341.01336852258413, (41, 12874): 340.5644092500172, (41, 12875): 340.07812338207185, (41, 12881): 341.3215995729494, (41, 12883): 341.25008958158725, (41, 12885): 340.41747797599925, (41, 12888): 340.3827246070105, (41, 12889): 339.54265582156086, (41, 12892): 341.06598163328977, (41, 12893): 341.25219161054366, (41, 12896): 340.406749113253, (41, 12906): 344.4240717187504, (41, 13018): 366.67310119906364, (41, 13071): 371.6184879110311, (41, 13131): 352.50384356949456, (41, 13146): 347.77689733149856, (41, 13159): 374.12476466677344, (41, 13193): 351.20928229395344, (41, 13198): 345.03831816314624, (41, 13292): 340.2905379324521, (41, 13296): 330.9040362031086, (41, 13406): 360.3261977053342, (41, 13407): 361.50167844149087, (41, 13417): 370.23090615162084, (41, 13418): 371.2806713320484, (41, 13438): 363.29443825206516, (41, 13442): 360.1871944999569, (41, 13443): 360.8035776599846, (41, 13764): 461.72512342735695, (41, 13766): 460.7322232854833, (41, 13771): 464.5026557218777, (41, 13783): 457.88585947408967, (41, 13784): 458.4409256298825, (41, 13792): 470.62214283580636, (41, 13824): 459.1356846010004, (41, 14017): 436.91046788499915, (41, 14870): 180.00635284816298, (41, 14997): 309.27831524866826, (41, 15000): 307.7328334196011, (41, 15003): 305.4465808648352, (41, 15006): 309.83952064103903, (41, 15007): 308.83319460554316, (41, 15056): 304.62368657988856, (41, 15063): 304.554850234272, (41, 15069): 303.21920313705607, (41, 15076): 307.67311361289063, (41, 15086): 312.21998987570777, (41, 15087): 311.1465519293661, (41, 15111): 315.192425668084, (41, 15116): 312.72266212509265, (41, 15722): 337.7642848797835, (41, 15998): 322.819922317973, (41, 16073): 671.2887202592025, (41, 16939): 715.7932167412771, (41, 16940): 713.8608423097508, (41, 16951): 717.5841325468344, (41, 16963): 717.3938207200164, (41, 16965): 719.0753327115539, (41, 16969): 719.4612602047762, (41, 16970): 717.7064449026706, (41, 16971): 716.1361641780925, (41, 16973): 716.579269147274, (41, 16974): 720.2772941461784, (41, 16976): 717.4805951272879, (41, 16978): 716.1409396154188, (41, 16980): 717.5932816400184, (41, 16982): 720.8369237322976, (41, 17045): 815.4502314497921, (41, 17048): 817.8597846196218, (41, 17304): 329.96357331527025, (41, 17305): 332.4372253197925, (41, 17330): 332.0675035316362, (41, 17334): 328.1761194243723, (41, 17343): 333.6211416691835, (41, 17345): 331.39063310042235, (41, 17347): 334.09778705979625, (41, 17351): 326.5266579718171, (41, 17372): 329.2746755476913, (41, 17373): 333.0523432261271, (41, 17377): 333.5848183866914, (41, 17382): 331.80702723986707, (41, 17383): 331.0463359977904, (41, 17389): 330.2668755395546, (41, 17400): 331.5360326142508, (41, 17401): 330.98427553600243, (41, 17402): 331.9550124728296, (41, 17403): 332.3961377314057, (41, 17440): 335.01040989278493, (41, 17455): 335.44760126824417, (41, 17491): 338.00441015187084, (41, 17507): 319.541872163135, (41, 17509): 319.55116414854217, (41, 17590): 329.6011766827991, (41, 17615): 303.8555557657275, (41, 17642): 306.3409616257305, (41, 17643): 307.55622170314706, (41, 17668): 303.01353028195723, (41, 17721): 293.83614857168163, (41, 17754): 299.2938072134917, (41, 17769): 316.04979949981384, (41, 17776): 318.81519908635937, (41, 17804): 316.81236354565146, (41, 17809): 317.6417142939842, (41, 17824): 314.99889363790294, (41, 17837): 322.4148631359521, (41, 17838): 324.355653256548, (41, 17862): 324.6391664362522, (41, 17866): 325.48606497816553, (41, 17872): 322.94127913137504, (41, 17873): 322.7382468241462, (41, 17881): 323.331838872351, (41, 17947): 547.7633259410669, (41, 17951): 545.7034784550384, (41, 17953): 544.7002927532134, (41, 17954): 544.4445544067689, (41, 17959): 548.3873057200499, (41, 17963): 548.719634833866, (41, 18000): 536.5754481929317, (41, 18001): 536.1755261746448, (41, 18111): 542.5378617256554, (41, 18148): 476.8582369253673, (41, 18166): 498.28535600888193, (41, 18189): 526.0075121145925, (41, 18239): 332.25098069995664, (41, 18240): 332.60247489234445, (41, 18245): 332.5173507953046, (41, 18247): 332.71694444013633, (41, 18251): 332.95409709754443, (41, 18256): 333.63227667891636, (41, 18258): 333.6277034856724, (41, 18259): 333.8604971344673, (41, 18260): 334.2150551360057, (41, 18262): 334.6233804411617, (41, 18263): 333.89386515785134, (41, 18264): 334.2236285160727, (41, 18266): 335.00769412086936, (41, 18267): 335.2792509425459, (41, 18268): 335.54734506939127, (41, 18269): 336.1267928617348, (41, 18275): 335.85505129062517, (41, 18285): 333.96911032856104, (41, 18308): 327.88546486340687, (41, 18313): 326.8478020364893, (41, 18314): 328.45466973560355, (41, 18315): 335.10093277731704, (41, 18316): 335.54758210719547, (41, 18317): 335.84911772106585, (41, 18320): 335.43424592513554, (41, 18321): 335.81789142779036, (41, 18322): 336.1950250775768, (41, 18324): 335.81434278003655, (41, 18325): 336.3183077792133, (41, 18326): 336.1082387283407, (41, 18327): 336.5282460501507, (41, 18329): 336.0062413141849, (41, 18330): 337.253576322896, (41, 18331): 336.6795177732411, (41, 18332): 336.3373524532609, (41, 18333): 336.772651094286, (41, 18336): 335.7687218377109, (41, 18337): 335.63190735640393, (41, 18403): 338.0835268903624, (41, 18432): 345.1670560449688, (41, 18451): 340.45664388986535, (41, 18466): 334.4755861246023, (41, 18481): 333.95083228266833, (41, 18483): 334.292771343049, (41, 18484): 333.7537395128662, (41, 18485): 331.7825316816464, (41, 18486): 331.2952875599804, (41, 18487): 330.2332392029323, (41, 18489): 332.3861902494544, (41, 18490): 332.09444696158704, (41, 18491): 332.3975618059716, (41, 18492): 329.878933239722, (41, 18493): 330.77537305759506, (41, 18494): 332.5420575500018, (41, 18495): 331.81704726774154, (41, 18496): 331.7831672214667, (41, 18497): 329.6684202875471, (41, 18498): 331.2238162344421, (41, 18499): 331.82390324349524, (41, 18501): 330.7788686599841, (41, 18502): 330.35519820797305, (41, 18503): 330.45177812815206, (41, 18504): 332.33380568555674, (41, 18506): 329.8407022926723, (41, 18507): 329.23882333668365, (41, 18508): 331.4051718315144, (41, 18509): 331.0848698840988, (41, 18510): 329.97770762595536, (41, 18511): 330.18403912576827, (41, 18512): 330.39147453688605, (41, 18515): 331.8797269038236, (41, 18516): 330.7725124855654, (41, 18517): 329.73969981536595, (41, 18518): 331.3907931549372, (41, 18519): 332.61476119172954, (41, 18520): 331.70554217253687, (41, 18522): 334.87504609828164, (41, 18523): 334.5737915577013, (41, 18532): 334.52613279978027, (41, 18535): 334.239927067407, (41, 18537): 334.0817291665747, (41, 18539): 333.9184087115868, (41, 18540): 333.72911243300143, (41, 18541): 333.63521024963245, (41, 18542): 333.6114994182468, (41, 18543): 333.5761678621241, (41, 18546): 332.95321331647335, (41, 18555): 333.1663964987371, (41, 18556): 332.9484570234204, (41, 18565): 334.0007097939753, (41, 18567): 333.3241289039461, (41, 18568): 333.5228461369516, (41, 18577): 334.5466326692113, (41, 18583): 335.4097542158301, (41, 18605): 336.8728218511165, (41, 18608): 331.8975287932471, (41, 18616): 337.7897639356988, (41, 18618): 337.9324876297146, (41, 18625): 340.40620710346747, (41, 18645): 340.7985875739052, (41, 18646): 340.08603608873835, (41, 18653): 336.77741551918876, (41, 18654): 337.31876818513854, (41, 18655): 336.395348170779, (41, 18666): 343.76543723059285, (41, 18837): 379.4623336927522, (41, 18974): 348.9676075195963, (41, 18999): 354.16881529905794, (41, 19000): 354.52255504786547, (41, 19174): 364.02924673149835, (41, 19342): 377.0013844386382, (41, 19455): 348.5877411896457, (41, 19555): 350.47300005898853, (41, 19564): 361.26477456073695, (41, 19573): 358.69003717372, (41, 19586): 356.8767462879034, (41, 19605): 355.3697133912047, (41, 19611): 356.7155650472443, (41, 19614): 353.2944812178837, (41, 19641): 363.8968227987354, (41, 19702): 366.92881492799046, (41, 19713): 365.4411893846907, (41, 19731): 333.9146344713638, (41, 19819): 353.26170234317414, (41, 19893): 187.46089999519253, (41, 19899): 176.67055371220792, (41, 19929): 187.01717748136159, (41, 19951): 175.13570516773336, (41, 19962): 181.35402822341368, (41, 19970): 188.0414153272495, (41, 19971): 185.79863263449676, (41, 19972): 185.22503230875085, (41, 19975): 187.23741645473805, (41, 19978): 183.02985531456403, (41, 19987): 184.36244732226245, (41, 19989): 187.03312552025494, (41, 20039): 184.6192438614574, (41, 20043): 185.65081701399495, (41, 20047): 188.2683425695123, (41, 20052): 189.4616009864933, (41, 20054): 188.25409347191956, (41, 20085): 191.33490625145797, (41, 20104): 191.30334667205418, (41, 20132): 189.70040038220986, (41, 20203): 168.45226081837131, (41, 20280): 163.68306235272087, (41, 20285): 161.46053203085887, (41, 20290): 164.26867906998623, (41, 20297): 165.9601563488458, (41, 20309): 166.68793894656758, (41, 20453): 172.72677593579962, (41, 20485): 176.2775418788692, (41, 20520): 181.07965131806677, (41, 20526): 176.18094871939218, (41, 20698): 535.8503603490885, (41, 20868): 580.2122243676558, (41, 21042): 283.08623823657143, (41, 21057): 283.71753842736456, (41, 21066): 280.5887764400998, (41, 21075): 284.4320660591369, (41, 21093): 279.324577620905, (41, 21098): 274.0420209313757, (41, 21127): 281.0964285866005, (41, 21130): 279.29081781472934, (41, 21144): 282.8636655703483, (41, 21146): 281.102748561375, (41, 21147): 283.9307181318891, (41, 21148): 282.7325455560828, (41, 21153): 296.5430598802805, (41, 21293): 279.21804575744045, (41, 21426): 313.9177936660704, (41, 21442): 322.1701458319734, (41, 21451): 322.8442072518114, (41, 21466): 316.0856072139069, (41, 21469): 315.60696074195965, (41, 21471): 316.407971738214, (41, 21473): 315.58441737695995, (41, 21475): 315.85425952452346, (41, 21482): 316.71893641609734, (41, 21484): 316.0735798491514, (41, 21488): 316.73218694006306, (41, 21494): 313.9053594047618, (41, 21498): 314.0393681596036, (41, 21500): 312.2902180600855, (41, 21514): 304.90510996147873, (41, 21537): 307.95669374224696, (41, 21662): 299.7025570919082, (41, 21691): 300.0165365832157, (41, 21757): 315.5672901994206, (41, 21777): 273.01897330896946, (41, 21778): 273.560892975146, (41, 21779): 271.5507457908406, (41, 21790): 274.2839356930786, (41, 21802): 270.9521597095274, (41, 21824): 268.7061812083335, (41, 21874): 269.31498472778856, (41, 21879): 266.52438144848713, (41, 21983): 281.7397864190449, (41, 22002): 265.6394174633076, (41, 22132): 308.90310375611693, (41, 22261): 378.54055495083816, (41, 22298): 372.7493029969762, (41, 22339): 384.8046231521392, (41, 22508): 349.51798777329367, (41, 22841): 896.4711984327918, (41, 22842): 896.1981699606348, (41, 22874): 890.5193341929686, (41, 22941): 891.9663457767587, (41, 22956): 894.5974051384273, (41, 22960): 896.1236562314639, (41, 22968): 895.0467690200326, (41, 22970): 896.4051267579645, (41, 22974): 895.3109668157787, (41, 22980): 898.729938810044, (41, 23025): 894.6939175069655, (41, 23028): 893.1578927045531, (41, 23081): 894.1837946042515, (41, 23104): 881.3477311861213, (41, 23147): 862.233190645997, (41, 23298): 296.00766443383776, (41, 23376): 294.7175401238884, (41, 23381): 285.2426316010397, (41, 23529): 289.6625190652123, (41, 23556): 290.0094575707314, (41, 23718): 302.4850068901931, (41, 24001): 307.74418360082046, (41, 24094): 296.47024859250837, (41, 24129): 298.633731907802, (41, 24174): 288.22195418416624, (41, 24235): 288.8510672046839, (41, 24259): 294.9884917096095, (41, 24260): 294.21670884189456, (41, 24261): 294.30434553658, (41, 24305): 299.32954228414843, (41, 24306): 298.9858135126803, (41, 24307): 298.7571414898798, (41, 24308): 322.8536511403981, (41, 24498): 317.587440543757, (41, 24499): 317.36073495820943, (41, 24500): 317.1863852592025, (41, 24668): 329.04823348777524, (41, 24711): 314.35981102818846, (41, 24756): 310.8548306035331, (41, 24788): 313.8553087248903, (41, 24809): 305.58183089372494, (41, 24813): 308.6046648528177, (41, 24821): 307.815784741222, (41, 24825): 307.51596947090013, (41, 24832): 305.7314974132594, (41, 24833): 306.4785706490557, (41, 24835): 306.956991495227, (41, 24837): 308.7823073789342, (41, 24840): 305.29249003442436, (41, 24841): 307.1168516310689, (41, 24844): 304.88805521967487, (41, 24845): 307.27894508244134, (41, 24846): 304.80597622648224, (41, 24849): 305.0037871978021, (41, 24850): 308.3008756678619, (41, 24863): 301.2451259487284, (41, 24866): 302.69314126310866, (41, 24885): 302.7678202282423, (41, 24886): 301.92920280439705, (41, 24889): 308.22463900873885, (41, 24903): 310.841964486297, (41, 24909): 308.325775601607, (41, 24999): 381.3487503502853, (41, 25019): 382.8736057251536, (41, 25028): 379.674169376584, (41, 25137): 135.99604073409895, (41, 25145): 135.9020418606381, (41, 25208): 113.1372899983002, (41, 25233): 112.09531261024269, (41, 25371): 151.26578876078628, (41, 25377): 156.29303501545965, (41, 25828): 212.9806517636605, (41, 25851): 231.9761419632753, (41, 25874): 218.4654604181408, (41, 25898): 206.42177613838177, (41, 25946): 214.6273990417584, (41, 26047): 176.7400913900316, (41, 26066): 197.195023855821, (41, 26197): 187.61872555495486, (41, 26212): 237.10338353624584, (41, 26253): 240.43926209338028, (41, 26254): 239.58127001306622, (41, 26257): 237.0284600341862, (41, 26258): 239.36084629632452, (41, 26260): 238.26164295785702, (41, 26266): 242.71352353044605, (41, 26267): 240.93751575143284, (41, 26271): 240.49537322182368, (41, 26304): 231.4232667770719, (41, 26305): 232.7054055768612, (41, 26363): 208.85396533457381, (41, 26441): 342.97433552198027, (41, 26442): 343.15245812407466, (41, 26450): 340.51246041890374, (41, 26459): 337.4124364643672, (41, 26462): 336.4990409716101, (41, 26467): 343.79734771652477, (41, 26471): 343.19402868018244, (41, 26472): 343.40262327309506, (41, 26473): 343.73026777682963, (41, 26476): 346.81456032704415, (41, 26485): 340.0824335598577, (41, 26493): 341.64847820620423, (41, 26524): 336.2975692559375, (41, 26525): 336.80279605791156, (41, 26556): 342.0658903925261, (41, 26560): 339.4204342363292, (41, 26561): 337.2834063861515, (41, 26564): 342.04931291245964, (41, 26569): 337.6941932568713, (41, 26570): 337.98742925200884, (41, 26573): 339.67646766679536, (41, 26581): 340.767436545301, (41, 26583): 339.5129116938926, (41, 26593): 342.23947426724413, (41, 26837): 345.457679617629, (41, 26844): 346.6088537788243, (41, 26863): 346.9128735092016, (41, 26893): 351.3533410704578, (41, 26902): 353.0297223719647, (41, 26905): 348.84270690699367, (41, 26912): 350.94300819420437, (41, 26921): 348.86021171781624, (41, 26922): 349.58347620142115, (41, 27212): 300.06043718868597, (41, 27218): 295.8931924458484, (41, 27239): 303.53885739178816, (41, 27257): 302.78744444067746, (41, 27274): 304.6046212540143, (41, 27279): 305.158428567083, (41, 27282): 303.34366103241604, (41, 27283): 302.3364962480783, (41, 27285): 305.9604119036159, (41, 27286): 305.83831117474455, (41, 27290): 301.94677151079406, (41, 27295): 299.50781706755805, (41, 27300): 304.5704176500651, (41, 27344): 303.7458114956223, (41, 27366): 306.64931728527466, (41, 27383): 307.97306964054644, (41, 27398): 308.05485607422685, (41, 27406): 305.5870171894133, (41, 27407): 305.4231889879894, (41, 27426): 297.0582516096059, (41, 27432): 291.05577248884157, (41, 27460): 293.9733972717948, (41, 27523): 321.2566924751689, (41, 27545): 338.92029523320946, (41, 27602): 391.26197148626653, (41, 27606): 391.205121011899, (41, 27646): 357.5450735822752, (41, 27667): 367.1034365886335, (41, 27672): 366.9722344816491, (41, 27674): 365.7266529320818, (41, 27688): 364.59476595445636, (41, 27692): 369.3684387469836, (41, 27693): 368.05718584379696, (41, 27705): 368.7054127966533, (41, 27712): 369.9602020819295, (41, 27786): 370.04458017512235, (41, 27790): 356.37667063012105, (41, 27791): 354.74823843458216, (41, 27795): 367.8850304753474, (41, 27801): 358.417915809525, (41, 27813): 372.5227240877937, (41, 27816): 369.08171405375595, (41, 27823): 357.9873693957231, (41, 27830): 365.004563423709, (41, 27884): 349.59824233483556, (41, 27885): 354.72562770792183, (41, 27896): 351.1737544742481, (41, 27919): 350.22222051586516, (41, 27922): 351.9263318801305, (41, 27930): 349.4159279148677, (41, 27934): 350.2546745384635, (41, 27935): 351.1364557206705, (41, 27948): 417.4101420993875, (41, 27951): 409.7538184368787, (41, 28061): 454.55624517170173, (41, 28290): 532.0783453423095, (41, 28292): 536.5284040907877, (41, 28293): 533.148760061796, (41, 28295): 533.9677781735143, (41, 28296): 532.8467939701471, (41, 28297): 529.8905001370866, (41, 28302): 530.6777966028479, (41, 28310): 678.4700925688353, (41, 28313): 682.6647348519572, (41, 28372): 678.0876722034492, (41, 28398): 678.6274057098618, (41, 28399): 678.2397865539014, (41, 28400): 679.5094037794119, (41, 28401): 675.5597594859026, (41, 28445): 683.0745981027994, (41, 28475): 669.5368902372242, (41, 28885): 265.2038370029289, (41, 28886): 263.8869244714348, (41, 28915): 260.1577027226062, (41, 28916): 261.17098508650037, (41, 28917): 260.13152500083515, (41, 28921): 266.6868913123518, (41, 28931): 265.5345028700852, (41, 28945): 250.42390295797318, (41, 28982): 255.28994784313085, (41, 29219): 235.0535078850146, (41, 29228): 234.88245648013572, (41, 29246): 226.64825592826176, (41, 29248): 222.37492261410966, (41, 29282): 222.90041479710638, (41, 29290): 231.26874492699966, (41, 29291): 229.98329606993806, (41, 29292): 230.58576806434777, (41, 29293): 230.51320021564015, (41, 29294): 228.7911054972138, (41, 29298): 229.41106727165112, (41, 29299): 228.28108667145548, (41, 29304): 230.71850106161665, (41, 29317): 232.17266852928185, (41, 29323): 232.41801790329544, (41, 29330): 231.499747344948, (41, 29331): 231.99337527977875, (41, 29344): 226.65064625242687, (41, 29445): 213.2442880861475, (41, 29724): 898.5237995726982, (41, 29738): 899.4228859500614, (41, 29745): 897.1590358974908, (41, 29748): 899.4849721967461, (41, 29750): 901.7118775828732, (41, 29759): 898.0296649675253, (41, 29772): 901.3873974341725, (41, 29781): 900.7059947290999, (41, 29784): 899.357333577874, (41, 29790): 901.7535692711195, (41, 29811): 900.6351168521868, (41, 29817): 911.428364009524, (41, 29818): 910.7900517207514, (41, 29929): 895.7058629315123, (41, 30039): 902.2038634236467, (41, 30066): 891.5579419454571, (41, 30116): 865.169245784692, (41, 30238): 825.3377407012312, (41, 30248): 839.7022147534985, (41, 30260): 839.6699828389427, (41, 30545): 275.6284420032079, (41, 30733): 282.09991072052077, (41, 30756): 262.0738236819576, (41, 30921): 268.3990123781848, (41, 31079): 391.8093742491565, (41, 31149): 376.5917826268529, (41, 31154): 379.1988309215893, (41, 31160): 376.26850398653613, (41, 31163): 379.21872523685346, (41, 31189): 374.96650704516867, (41, 31215): 377.5428093129532, (41, 31259): 389.1641643886496, (41, 31262): 388.1399576222452, (41, 31430): 399.8119427021224, (41, 31568): 419.7012122625736, (41, 31751): 397.1496342694093, (42, 109): 272.5272789733887, (42, 872): 732.8075572089596, (42, 873): 735.2658280229178, (42, 877): 734.3600103809372, (42, 879): 734.7262469466431, (42, 884): 732.2924669343106, (42, 889): 733.8254548354697, (42, 891): 731.4748671118818, (42, 892): 736.6284186380016, (42, 894): 736.3114332030053, (42, 896): 733.9153872668825, (42, 903): 734.4707268600669, (42, 909): 730.2310861698095, (42, 910): 731.1999551395722, (42, 912): 729.5774034807995, (42, 913): 727.7953679231404, (42, 916): 727.0179731388454, (42, 926): 731.9856789291604, (42, 927): 731.1564413217317, (42, 948): 730.5812949861502, (42, 961): 731.9343319173507, (42, 962): 732.2025617866371, (42, 963): 732.5074866313915, (42, 967): 735.5034877693253, (42, 974): 734.2214799060376, (42, 998): 736.4892003510564, (42, 1014): 790.0065710266107, (42, 1086): 726.1702578122246, (42, 1087): 725.7623578653125, (42, 1089): 723.5386871708341, (42, 1090): 724.5861984597303, (42, 1092): 728.1406581329328, (42, 1097): 725.4486481972152, (42, 1107): 729.8483171147844, (42, 1387): 353.22529737992704, (42, 1554): 315.06238920185837, (42, 1827): 844.9223633524026, (42, 1828): 845.1874901348718, (42, 1829): 845.5602670298183, (42, 1830): 845.1482729143816, (42, 1831): 845.3724718748346, (42, 1832): 845.110955955795, (42, 1833): 845.1446725006388, (42, 1836): 844.8666335382567, (42, 1841): 846.4314130771729, (42, 1843): 845.7733211788781, (42, 1844): 846.0621955558927, (42, 1845): 845.2750234663818, (42, 1847): 842.750572543718, (42, 1848): 843.622580694427, (42, 1849): 847.7047323765001, (42, 1850): 848.1365595849862, (42, 1851): 844.2790077604544, (42, 1852): 844.3332253174162, (42, 1854): 844.7584265310263, (42, 1856): 842.6143592503779, (42, 1857): 843.557984143207, (42, 1858): 847.3141981744583, (42, 1861): 845.4973434053165, (42, 1866): 842.5505063351201, (42, 1867): 846.4846906765802, (42, 1868): 845.963764092923, (42, 1870): 845.9772057410142, (42, 1871): 846.3729869566856, (42, 1875): 844.7206100826135, (42, 1880): 843.1689923668807, (42, 1882): 843.4134496095496, (42, 1883): 848.1812458865842, (42, 1889): 843.6400784069432, (42, 1893): 845.6220576334595, (42, 1894): 845.0066216738018, (42, 1899): 843.1011964160916, (42, 1900): 843.5593013683322, (42, 1902): 846.6939010394282, (42, 1905): 847.4850384479812, (42, 1907): 844.2255886256913, (42, 1910): 844.5300469677767, (42, 1917): 849.189188777864, (42, 1920): 844.2929419025496, (42, 1935): 847.6100780382783, (42, 1937): 848.2863990094926, (42, 1946): 841.7459295497364, (42, 1949): 842.5096512353699, (42, 1950): 839.8221304673631, (42, 1951): 841.1151588733279, (42, 1952): 842.0601017800864, (42, 1953): 842.4968583625581, (42, 1954): 841.877097465128, (42, 1958): 842.2861891441123, (42, 1960): 843.5731185648035, (42, 1968): 844.0809556398584, (42, 1969): 847.7800448007011, (42, 1974): 846.8116877343873, (42, 1975): 846.797448590979, (42, 1979): 844.9700290254185, (42, 1980): 844.8151322002919, (42, 1981): 845.3582605953185, (42, 1985): 845.8029250039476, (42, 1994): 838.7557293800102, (42, 2011): 843.3761562997702, (42, 2019): 849.7592940700645, (42, 2020): 848.9152977614882, (42, 2029): 845.6959853867139, (42, 2030): 848.3304988656355, (42, 2032): 845.1620054888238, (42, 2033): 846.8795626255373, (42, 2034): 846.8424339323459, (42, 2036): 843.5930908949064, (42, 2037): 844.4263367889375, (42, 2038): 844.7393763865773, (42, 2042): 854.4936835374724, (42, 2050): 846.450701924608, (42, 2051): 846.302250703756, (42, 2053): 846.5645995985379, (42, 2054): 847.4274796767387, (42, 2066): 845.6701398563072, (42, 2067): 845.6796399127163, (42, 2071): 837.1300927779358, (42, 2072): 838.7527365455051, (42, 2073): 834.3210058940018, (42, 2074): 834.0991208129642, (42, 2080): 831.3575692707044, (42, 2082): 839.626614535528, (42, 2083): 840.4659644397461, (42, 2089): 838.6918146695494, (42, 2090): 839.475359812837, (42, 2092): 838.4112514583663, (42, 2098): 832.4083310092902, (42, 2099): 833.3500939028471, (42, 2101): 832.2359054789969, (42, 2102): 836.6580009044231, (42, 2103): 835.2668128594652, (42, 2104): 834.5050097663515, (42, 2106): 841.0301606488895, (42, 2112): 832.8221119021925, (42, 2113): 837.2863715195921, (42, 2114): 838.3489164339586, (42, 2117): 841.6915384993321, (42, 2123): 835.114253936566, (42, 2124): 836.025622368642, (42, 2134): 833.4544126842351, (42, 2138): 836.1259868253147, (42, 2141): 833.7625239692733, (42, 2148): 835.1818013652447, (42, 2150): 831.5489903856923, (42, 2151): 832.5153416588861, (42, 2152): 831.0516416933523, (42, 2153): 835.4824463565479, (42, 2154): 831.7010691277729, (42, 2155): 831.2788768717538, (42, 2156): 830.5672430485283, (42, 2157): 831.5671361935142, (42, 2160): 837.4456977590137, (42, 2161): 830.903830937007, (42, 2162): 835.6681056728586, (42, 2163): 834.385340413774, (42, 2164): 834.3036147339775, (42, 2168): 831.96453361179, (42, 2172): 832.8522782575853, (42, 2174): 832.4170548768531, (42, 2178): 833.6099444136786, (42, 2179): 833.0229918944227, (42, 2183): 836.0752566250662, (42, 2185): 836.1387419756529, (42, 2186): 835.408015258078, (42, 2190): 837.6143819895506, (42, 2192): 836.3008585637848, (42, 2193): 836.3273272568171, (42, 2194): 834.9854461983276, (42, 2195): 834.8045815221442, (42, 2197): 836.5945730247134, (42, 2205): 834.7343978362891, (42, 2207): 832.3093549174622, (42, 2208): 833.6680935169708, (42, 2212): 836.6890241693001, (42, 2214): 809.8138013215158, (42, 2225): 813.044499384732, (42, 2231): 806.479555134816, (42, 2278): 826.393694423311, (42, 2284): 829.1495683979894, (42, 2285): 828.764587343046, (42, 2291): 823.2912798790543, (42, 2292): 823.8920787160962, (42, 2307): 827.3590467858363, (42, 2313): 822.6403807421708, (42, 2317): 821.8554982027316, (42, 2319): 824.839871154963, (42, 2321): 826.1042747148684, (42, 2323): 825.9383217259915, (42, 2326): 830.7554846141289, (42, 2327): 829.5626770892691, (42, 2329): 828.7486037845912, (42, 2330): 827.821357829422, (42, 2332): 829.7864268348377, (42, 2344): 826.7437013021145, (42, 2346): 826.6887856134335, (42, 2361): 826.2046762797046, (42, 2368): 840.1364965863667, (42, 2374): 841.4503808271983, (42, 2375): 841.8891478841607, (42, 2377): 837.3037515787214, (42, 2378): 842.7166019926559, (42, 2379): 842.8324900382092, (42, 2380): 843.285016083642, (42, 2383): 838.5258496253687, (42, 2385): 839.2331388263084, (42, 2395): 839.3100867384073, (42, 2397): 842.2874561080308, (42, 2398): 835.8429412054758, (42, 2399): 837.4918158751651, (42, 2400): 837.121852787125, (42, 2402): 839.7426061366268, (42, 2403): 840.7671680557971, (42, 2404): 841.0312945586405, (42, 2405): 838.56195025808, (42, 2407): 840.5737074300386, (42, 2408): 841.776032198344, (42, 2409): 839.3110381282397, (42, 2411): 840.7577141975099, (42, 2412): 840.4898214166733, (42, 2413): 841.3299551114844, (42, 2414): 839.9632127186982, (42, 2422): 840.4446876471102, (42, 2424): 840.7794945137209, (42, 2426): 841.0018725377192, (42, 2433): 839.0913075751499, (42, 2436): 838.5814968676448, (42, 2437): 832.5998270077849, (42, 2440): 833.9186061902368, (42, 2445): 860.3104683763006, (42, 2447): 857.070512847066, (42, 2454): 860.1298741389163, (42, 2455): 860.3084459446425, (42, 2460): 850.79669521464, (42, 2461): 851.9689106532636, (42, 2471): 870.8639053443578, (42, 2492): 850.0506388924074, (42, 2511): 840.7167326019982, (42, 2523): 845.4894099796031, (42, 2525): 844.0044551934664, (42, 2535): 846.9478788147866, (42, 2537): 844.8357251459867, (42, 2538): 846.3147584206824, (42, 2539): 845.5910599282394, (42, 2540): 847.9033339159672, (42, 2542): 849.3945325541432, (42, 2559): 879.5019811760243, (42, 2575): 876.6719388160394, (42, 2599): 831.6831248241355, (42, 2600): 841.7609742726357, (42, 2607): 836.00294327319, (42, 2627): 846.0499438978219, (42, 2647): 851.4888133732884, (42, 2674): 848.8137145458805, (42, 2681): 847.9572558159556, (42, 2683): 850.7048758608328, (42, 2686): 847.6349607351436, (42, 2689): 883.6961303678769, (42, 2690): 883.8503412305017, (42, 2713): 890.1678045064533, (42, 2714): 890.6803866504382, (42, 2715): 891.5738674607303, (42, 2739): 890.8094611722312, (42, 2740): 885.4323410340099, (42, 2741): 885.8946479318769, (42, 2749): 889.4749711145193, (42, 2750): 889.7883279329964, (42, 2752): 890.4408213629002, (42, 2755): 891.1258510867024, (42, 2758): 890.8910338852646, (42, 2759): 890.9094244579084, (42, 2769): 889.9103428240624, (42, 2771): 886.8084465429565, (42, 2779): 886.8466758396675, (42, 2784): 876.6855411816423, (42, 2800): 878.2364098191442, (42, 2802): 883.5778903992042, (42, 2803): 883.2673417378182, (42, 2804): 882.6820254486669, (42, 2805): 884.2411899925115, (42, 2807): 884.2154193608195, (42, 2809): 883.8158557986741, (42, 2812): 878.1596775033431, (42, 2814): 883.3113706090527, (42, 2817): 883.2245022066675, (42, 2819): 884.4046846479613, (42, 2823): 878.4541654304619, (42, 2832): 885.3083518073752, (42, 2836): 881.2899986077642, (42, 2839): 884.2328025714162, (42, 2841): 883.5683134820532, (42, 2843): 883.320327457924, (42, 2846): 881.9599579684963, (42, 2849): 885.8840212446966, (42, 2852): 884.9909833288385, (42, 2853): 886.2931614077155, (42, 2876): 886.5552691728379, (42, 2877): 889.7569272335177, (42, 2885): 890.4263059926232, (42, 2918): 885.0444349030464, (42, 2921): 886.3979012922462, (42, 2925): 880.1265409794867, (42, 2926): 878.0740444491612, (42, 2930): 882.5550762122588, (42, 2931): 880.6539788411127, (42, 2938): 885.0135250010694, (42, 2940): 889.2651264423502, (42, 2947): 884.5849242973694, (42, 2949): 882.6235693245237, (42, 2950): 883.199911926475, (42, 2952): 882.5140090501716, (42, 2958): 882.4000092452558, (42, 2959): 883.1140518501568, (42, 2960): 884.6207785140258, (42, 2961): 883.8672594172468, (42, 2963): 881.7927706546318, (42, 2968): 882.2001703181769, (42, 2976): 881.6392772204075, (42, 2981): 868.2667704252584, (42, 2982): 867.8323906113076, (42, 2984): 867.1409543593473, (42, 3003): 865.8844414458305, (42, 3046): 857.6417512804483, (42, 3050): 864.3283883623017, (42, 3051): 864.8855537165571, (42, 3053): 863.366419643697, (42, 3069): 871.6356943441687, (42, 3071): 863.1291533362667, (42, 3080): 890.3356187586792, (42, 3199): 863.302211354027, (42, 3200): 861.6800218259264, (42, 3205): 871.4586320641592, (42, 3209): 862.4990938811098, (42, 3215): 861.8110148227496, (42, 3217): 859.855635513352, (42, 3249): 862.0235439816461, (42, 3263): 876.8020032161875, (42, 3289): 866.7784757227217, (42, 3301): 867.1646174215529, (42, 3302): 866.4909071855942, (42, 3307): 865.6218831665127, (42, 3310): 868.0062080603295, (42, 3391): 867.9694827477664, (42, 3509): 554.1130495377025, (42, 3510): 552.723371352145, (42, 3511): 553.6880871944812, (42, 3512): 552.8625454840861, (42, 3514): 553.1853291751363, (42, 3519): 557.1785690536643, (42, 3536): 556.6334615843119, (42, 3545): 558.853312030354, (42, 3548): 556.7723468554495, (42, 3572): 557.3753921892176, (42, 3581): 555.5603597464302, (42, 3583): 554.7760140049977, (42, 3601): 559.7265140475073, (42, 3656): 557.3153147125771, (42, 3669): 554.254810575453, (42, 3670): 555.4864742976202, (42, 3695): 548.5102233914032, (42, 3696): 549.5009983938359, (42, 3782): 557.8993408603467, (42, 3792): 556.2817726140134, (42, 3989): 59.357145187163106, (42, 4008): 66.42989982091646, (42, 4031): 69.37587298636555, (42, 4045): 63.59933364006506, (42, 4144): 60.90667632622165, (42, 4145): 50.38780319150079, (42, 4164): 57.33891613294688, (42, 4168): 53.5641335017279, (42, 4173): 52.36122526126743, (42, 4181): 47.930328425094515, (42, 4228): 47.583461527027715, (42, 4248): 40.75884437782067, (42, 4254): 24.0, (42, 4260): 24.0, (42, 4262): 24.0, (42, 4273): 24.0, (42, 4319): 42.57161635698244, (42, 4326): 43.02775652381899, (42, 4328): 42.260575140053845, (42, 4334): 41.97933480060649, (42, 4335): 42.88504685195481, (42, 4372): 272.6307291634736, (42, 4413): 286.58049935179463, (42, 4434): 270.6438450731936, (42, 4447): 266.38724464427895, (42, 4452): 271.5551335062076, (42, 4463): 294.3720626189505, (42, 4465): 292.59074758629157, (42, 4619): 303.84978973256773, (42, 4645): 301.78234230260705, (42, 4657): 303.7479359072376, (42, 4666): 305.3891902152466, (42, 4676): 305.6681588904902, (42, 4678): 304.77108257566147, (42, 4689): 306.9874773889927, (42, 4704): 309.2270754836616, (42, 4726): 360.6787552555162, (42, 4727): 359.88754896806836, (42, 4730): 358.2239920269463, (42, 4731): 359.5687241565451, (42, 4734): 355.4671004225606, (42, 4735): 355.46627709875924, (42, 4736): 356.49371888236493, (42, 4737): 356.0501089769114, (42, 4738): 356.75198196439203, (42, 4756): 357.9394049366183, (42, 4760): 350.32576226087764, (42, 4761): 349.2965752565141, (42, 4762): 350.14770808317525, (42, 4765): 351.1528745025647, (42, 4773): 361.5150807005686, (42, 4774): 362.00215055278335, (42, 4790): 360.80954177393113, (42, 4795): 359.81869897015116, (42, 4799): 362.9760171436996, (42, 4801): 366.2639186024116, (42, 4804): 358.59203017679744, (42, 4805): 357.79504784212264, (42, 4806): 363.46061262800055, (42, 4815): 363.7530214647697, (42, 4816): 365.1893965065895, (42, 4817): 366.950858905706, (42, 4826): 365.35105506677354, (42, 4830): 364.8156626413367, (42, 4839): 352.6838356191926, (42, 4840): 353.9806055059574, (42, 4841): 352.80669346709743, (42, 4846): 352.02838843503156, (42, 4848): 353.04748851424364, (42, 4850): 353.96372006958757, (42, 4871): 339.4235168448816, (42, 4883): 347.69628335412693, (42, 4900): 341.7393804390596, (42, 4901): 341.7341707853297, (42, 4917): 327.5061492214774, (42, 4931): 324.17582486435356, (42, 4944): 326.99228341053777, (42, 4956): 325.6753402750597, (42, 4958): 327.351848668278, (42, 4959): 327.94221609348847, (42, 4961): 325.62084308763326, (42, 4966): 325.9002108423672, (42, 5207): 322.5250885225165, (42, 5272): 227.5257785065446, (42, 5283): 228.19588372209626, (42, 5287): 233.46124022606028, (42, 5289): 233.9469753784461, (42, 5293): 223.63129450496592, (42, 5295): 224.9542014363955, (42, 5296): 227.46933875071173, (42, 5298): 228.86088507687074, (42, 5303): 231.47346777368082, (42, 5305): 232.11772663859614, (42, 5306): 235.3050257374597, (42, 5307): 232.0924954324554, (42, 5308): 233.15274136148292, (42, 5313): 229.97015906906705, (42, 5314): 229.32212109096267, (42, 5317): 234.79390693099464, (42, 5319): 231.55906609478433, (42, 5324): 229.33204911414222, (42, 5326): 227.7610977419606, (42, 5348): 237.35120939184299, (42, 5351): 241.21619942308962, (42, 5399): 237.97041097808872, (42, 5413): 247.4486524702448, (42, 5422): 235.75699160750267, (42, 5445): 235.65091283443377, (42, 5448): 235.2201959690322, (42, 5456): 237.788181079513, (42, 5467): 238.90242123391937, (42, 5624): 227.28062500827755, (42, 5671): 208.78625377104632, (42, 5672): 207.27813306562186, (42, 5797): 228.02416036453678, (42, 5871): 271.66571400437056, (42, 5976): 264.409050033203, (42, 6118): 719.4723224765204, (42, 6248): 748.3707751800531, (42, 6345): 241.05697525677775, (42, 6352): 247.80702301705082, (42, 6354): 239.35239477168625, (42, 6359): 238.12569325529222, (42, 6376): 247.04774378524144, (42, 6378): 240.16180925069224, (42, 6381): 238.75269320216856, (42, 6383): 242.44344600093, (42, 6396): 240.02514204052008, (42, 6399): 241.10731549096806, (42, 6408): 247.44626763877022, (42, 6409): 244.01736359005156, (42, 6419): 254.47472771408235, (42, 6422): 246.34531087980457, (42, 6423): 246.87314292123835, (42, 6424): 239.73860607403813, (42, 6439): 240.95210832836392, (42, 6464): 242.73707118176833, (42, 6465): 243.4774116917955, (42, 6469): 242.8150317062637, (42, 6470): 243.2701188675241, (42, 6472): 235.8844727675294, (42, 6480): 236.87166284887286, (42, 6486): 232.64760546566066, (42, 6497): 234.0248399637873, (42, 6503): 241.96168387320148, (42, 6508): 241.6527736675381, (42, 6509): 240.29299269270558, (42, 6521): 235.89480127561782, (42, 6544): 236.18598340334427, (42, 6552): 244.80035221963288, (42, 6553): 245.813254689403, (42, 6554): 246.84644583289202, (42, 6578): 243.1367809714182, (42, 6582): 243.70572914739904, (42, 6601): 242.62816294695062, (42, 6609): 234.66768589188405, (42, 6610): 234.3216257123802, (42, 6611): 234.26643673204222, (42, 6614): 234.89774581345932, (42, 6615): 234.65080968916533, (42, 6616): 233.38703363971433, (42, 6617): 233.9207391024257, (42, 6618): 232.23477533429374, (42, 6619): 235.61026752918625, (42, 6620): 233.28347164920785, (42, 6621): 234.13988918255458, (42, 6622): 233.99069037420622, (42, 6623): 234.88138327590295, (42, 6624): 235.56173954273086, (42, 6625): 235.7754505518207, (42, 6626): 235.70478705866446, (42, 6627): 235.2074875814743, (42, 6628): 233.38874350156496, (42, 6629): 235.21403957446046, (42, 6630): 236.68816311521712, (42, 6632): 235.34965654435362, (42, 6634): 237.56736459765654, (42, 6635): 234.49627871095282, (42, 6636): 233.3088766368203, (42, 6637): 236.40408004690272, (42, 6638): 236.4836036699538, (42, 6639): 235.05329107582037, (42, 6640): 236.3873827640605, (42, 6641): 234.10425733830348, (42, 6642): 236.3988398773162, (42, 6643): 235.88139553584756, (42, 6645): 235.44175967115862, (42, 6646): 232.6095728156567, (42, 6647): 236.17057070094444, (42, 6653): 234.7217911974764, (42, 6655): 235.07840540083598, (42, 6658): 237.5930319718857, (42, 6662): 236.38359413320728, (42, 6819): 285.40573567503816, (42, 6996): 268.86225155140596, (42, 7059): 257.3595194848798, (42, 7187): 282.70247274021483, (42, 7304): 302.7721330106302, (42, 7528): 271.46264797106716, (42, 7720): 202.2157067325161, (42, 7793): 204.55661862691935, (42, 7807): 203.29533802293597, (42, 7808): 205.14879977021687, (42, 7831): 227.86651978212188, (42, 7850): 217.07111439785965, (42, 7852): 219.7254462041253, (42, 8012): 204.576861792947, (42, 8125): 205.3601646927661, (42, 8208): 181.67083251370138, (42, 8392): 219.81646638535494, (42, 8651): 341.2054094143193, (42, 9088): 291.16968370180984, (42, 9443): 371.5835028813715, (42, 9444): 370.1165827805557, (42, 9828): 425.8682812885089, (42, 9868): 423.1985969197997, (42, 10180): 205.5693992941547, (42, 10256): 181.2416923659721, (42, 10276): 189.788810873329, (42, 10378): 179.7689318596717, (42, 10676): 226.9041441453197, (42, 10714): 246.78492631625508, (42, 10730): 234.1434702091704, (42, 10862): 386.0307112367811, (42, 10881): 384.96154003854707, (42, 10883): 385.7791928139277, (42, 10885): 386.09061869331026, (42, 10891): 387.06706905699104, (42, 10909): 385.49152548109964, (42, 10911): 383.62880398592216, (42, 10913): 384.42871851227534, (42, 10915): 383.55741724151375, (42, 10919): 382.6663644120344, (42, 11037): 411.1786693941018, (42, 11039): 407.17850523532394, (42, 11516): 165.74092371119448, (42, 11856): 41.513350955617724, (42, 11857): 44.79409501391548, (42, 11861): 43.17543234518567, (42, 11881): 40.924551798166824, (42, 11902): 44.7446109103363, (42, 11911): 43.53447904591622, (42, 11914): 43.78704784212748, (42, 11922): 41.56706606000751, (42, 11924): 40.112460603902015, (42, 11926): 41.09621637146937, (42, 11950): 36.59569088618744, (42, 11963): 33.32631031278158, (42, 11983): 32.276445652139415, (42, 11985): 32.05941523430026, (42, 12009): 29.27683510480582, (42, 12010): 32.4899889415423, (42, 12018): 31.678615321290618, (42, 12020): 31.429867767625108, (42, 12021): 30.685727543743546, (42, 12024): 28.420307015768028, (42, 12025): 29.84378568350934, (42, 12027): 30.196569196873575, (42, 12031): 32.933745961830034, (42, 12032): 32.5676447914218, (42, 12035): 28.73689295828446, (42, 12041): 34.071593486156466, (42, 12045): 68.85202398464237, (42, 12145): 47.92919629631675, (42, 12275): 69.76812267530022, (42, 12294): 70.7114547975283, (42, 12358): 89.07921794335644, (42, 12463): 99.99848039340871, (42, 12465): 100.04868498870978, (42, 12482): 99.4551501412607, (42, 12503): 99.90337871868908, (42, 12506): 100.65705990902308, (42, 12549): 94.89041353576809, (42, 12559): 95.11843106624771, (42, 12569): 97.20937289197276, (42, 12572): 97.69610073962805, (42, 12574): 96.22501575013716, (42, 12576): 95.08777009139807, (42, 12591): 92.68584627317911, (42, 12608): 96.26298680940901, (42, 12696): 86.65375314630845, (42, 12710): 88.7623201207577, (42, 12728): 89.25077614501606, (42, 12766): 152.1716015544125, (42, 12771): 155.1242268344146, (42, 12790): 156.42852870714992, (42, 12795): 160.0228683070433, (42, 12797): 168.18141828510508, (42, 12798): 166.51863706418487, (42, 12811): 158.07242350353988, (42, 12830): 161.70444412053783, (42, 12848): 158.59879118955027, (42, 12850): 156.94261930427714, (42, 12852): 161.6084014118694, (42, 12854): 162.91557855197547, (42, 12859): 156.87396037885117, (42, 12861): 164.71317273261727, (42, 12865): 157.23236789864166, (42, 12866): 157.3916813067598, (42, 12867): 155.26466588776626, (42, 12874): 156.36240345735789, (42, 12875): 155.1671917743892, (42, 12881): 159.7585646174268, (42, 12883): 158.10150461784858, (42, 12885): 154.43820397630418, (42, 12888): 158.5099147339412, (42, 12889): 158.5485730122445, (42, 12892): 156.28329779940478, (42, 12893): 158.79719627079825, (42, 12896): 157.67289024230215, (42, 12906): 157.8784833323383, (42, 13018): 179.6252660470262, (42, 13071): 182.06202055447596, (42, 13131): 183.0749845963419, (42, 13146): 172.71464679767752, (42, 13159): 195.91704308469727, (42, 13193): 184.20532693836424, (42, 13198): 197.07272129652551, (42, 13292): 178.05534589255728, (42, 13296): 170.1049758074221, (42, 13406): 211.4666073806213, (42, 13407): 212.36857392301715, (42, 13417): 216.78161795687, (42, 13418): 215.6698599037006, (42, 13438): 206.19920005289362, (42, 13442): 203.74476044592902, (42, 13443): 205.20601425411198, (42, 13764): 345.21150932014484, (42, 13766): 343.41977629039536, (42, 13771): 346.42138416054087, (42, 13783): 344.67441606392975, (42, 13784): 340.92964284244823, (42, 13792): 351.7882665624334, (42, 13824): 346.1478223889574, (42, 14017): 328.9176102762931, (42, 14870): 350.811124561306, (42, 14997): 291.6460449606334, (42, 15000): 291.67196305938006, (42, 15003): 290.69070307434504, (42, 15006): 287.1310412223405, (42, 15007): 285.9375756314562, (42, 15056): 286.6872675655197, (42, 15063): 287.89044777710365, (42, 15069): 288.5441717819744, (42, 15076): 285.8788085472121, (42, 15086): 289.4519997262828, (42, 15087): 291.01150072587984, (42, 15111): 294.47617830552554, (42, 15116): 292.5024418199921, (42, 15722): 324.61781578044605, (42, 15998): 352.1907576969783, (42, 16073): 609.8015177074755, (42, 16939): 766.9825415430192, (42, 16940): 765.1844064154483, (42, 16951): 767.1753248902888, (42, 16963): 767.3622255338449, (42, 16965): 769.5751035769302, (42, 16969): 769.0083039589008, (42, 16970): 768.1742562729871, (42, 16971): 766.1824850504388, (42, 16973): 766.0286426482821, (42, 16974): 770.4453749865551, (42, 16976): 768.3411811148085, (42, 16978): 766.8929794546112, (42, 16980): 769.0938333066515, (42, 16982): 770.4086547321954, (42, 17045): 828.8599392209394, (42, 17048): 831.4164115425223, (42, 17304): 26.421653513910027, (42, 17305): 27.936292526103365, (42, 17330): 28.01657938188106, (42, 17334): 24.098846972109666, (42, 17343): 29.895843956252378, (42, 17345): 26.69530126844535, (42, 17347): 29.621067312179505, (42, 17351): 24.0, (42, 17372): 24.87850418995674, (42, 17373): 29.40315701987863, (42, 17377): 29.928398191321087, (42, 17382): 27.526816238192044, (42, 17383): 27.102018727447156, (42, 17389): 25.904649384785262, (42, 17400): 27.941262071796512, (42, 17401): 27.5047186377491, (42, 17402): 28.32490838944412, (42, 17403): 28.770872645171682, (42, 17440): 29.918004481359315, (42, 17455): 31.188742792416402, (42, 17491): 33.415468710424285, (42, 17507): 24.0, (42, 17509): 24.0, (42, 17590): 24.23997813405414, (42, 17615): 24.0, (42, 17642): 24.0, (42, 17643): 24.0, (42, 17668): 24.0, (42, 17721): 24.0, (42, 17754): 24.0, (42, 17769): 24.0, (42, 17776): 24.0, (42, 17804): 24.0, (42, 17809): 24.0, (42, 17824): 24.0, (42, 17837): 24.0, (42, 17838): 24.0, (42, 17862): 24.0, (42, 17866): 24.0, (42, 17872): 24.0, (42, 17873): 24.0, (42, 17881): 24.0, (42, 17947): 619.0567932488731, (42, 17951): 615.6712883350996, (42, 17953): 614.9905223198775, (42, 17954): 615.2051186144337, (42, 17959): 618.4194208596346, (42, 17963): 617.2843361147587, (42, 18000): 599.9622427835297, (42, 18001): 600.5974511569516, (42, 18111): 647.3287261158949, (42, 18148): 560.2951361338662, (42, 18166): 593.8145954811879, (42, 18189): 625.4131296349916, (42, 18239): 29.134254772968667, (42, 18240): 29.378616003288943, (42, 18245): 29.38973430792855, (42, 18247): 29.38564444556757, (42, 18251): 29.702319656005507, (42, 18256): 30.352696992248266, (42, 18258): 30.186155112388835, (42, 18259): 30.388489279136422, (42, 18260): 30.71537145650788, (42, 18262): 31.13776593987031, (42, 18263): 30.588045326669455, (42, 18264): 30.894314765483763, (42, 18266): 31.47363586065432, (42, 18267): 31.73732936374769, (42, 18268): 31.969434042368647, (42, 18269): 32.52516857851121, (42, 18275): 32.26414090323072, (42, 18285): 30.685307519200013, (42, 18308): 24.97477871848847, (42, 18313): 24.0, (42, 18314): 25.093037857230406, (42, 18315): 31.743902863944896, (42, 18316): 32.06912268961509, (42, 18317): 32.35140095539108, (42, 18320): 32.09135358978718, (42, 18321): 32.40902969497429, (42, 18322): 32.779211302578645, (42, 18324): 32.5663654066468, (42, 18325): 33.21945096221963, (42, 18326): 32.95946996848847, (42, 18327): 32.91823279731108, (42, 18329): 33.12380817209954, (42, 18330): 33.90078439059128, (42, 18331): 33.28930322145861, (42, 18332): 32.84778959344129, (42, 18333): 33.51203300829384, (42, 18336): 32.612552369081385, (42, 18337): 32.61055646868522, (42, 18403): 34.328457545928615, (42, 18432): 39.7579982384472, (42, 18451): 35.50392903479582, (42, 18466): 33.19468701072163, (42, 18481): 30.98007042704934, (42, 18483): 31.225473988668604, (42, 18484): 30.673904120048185, (42, 18485): 28.7660849061795, (42, 18486): 28.91622837435724, (42, 18487): 27.772834354335647, (42, 18489): 29.6042774367789, (42, 18490): 29.831464219438836, (42, 18491): 30.239672114758267, (42, 18492): 27.098371923569918, (42, 18493): 28.500487008451618, (42, 18494): 29.635881349740885, (42, 18495): 29.49351623780394, (42, 18496): 29.2564847485558, (42, 18497): 27.3000936017762, (42, 18498): 28.43938860850418, (42, 18499): 29.156675132238227, (42, 18501): 28.22373601351697, (42, 18502): 27.736686524327332, (42, 18503): 27.648518395757808, (42, 18504): 29.712623017636368, (42, 18506): 27.641048314653805, (42, 18507): 27.049508042034628, (42, 18508): 28.829141716530273, (42, 18509): 28.61856910332782, (42, 18510): 27.33291445844318, (42, 18511): 28.186848464912458, (42, 18512): 28.064462174367385, (42, 18515): 29.42423164501239, (42, 18516): 28.716363508674416, (42, 18517): 27.7860594151061, (42, 18518): 29.291042944311265, (42, 18519): 29.947485899766153, (42, 18520): 28.97509817462922, (42, 18522): 32.32623700139472, (42, 18523): 32.16054595700825, (42, 18532): 32.40486661942748, (42, 18535): 31.641635725197872, (42, 18537): 31.229626514393104, (42, 18539): 31.176892003400738, (42, 18540): 31.080238372844725, (42, 18541): 31.168787926353392, (42, 18542): 31.252085596630863, (42, 18543): 30.74680293688619, (42, 18546): 30.54576966599912, (42, 18555): 31.205313401627386, (42, 18556): 31.16286481346735, (42, 18565): 32.01857697844988, (42, 18567): 31.7406107373446, (42, 18568): 31.572499766690907, (42, 18577): 34.45072513462884, (42, 18583): 34.56383785641133, (42, 18605): 35.93004141708847, (42, 18608): 31.07190186868103, (42, 18616): 38.65225341648608, (42, 18618): 40.805433751635555, (42, 18625): 41.386759794571184, (42, 18645): 40.023961142891444, (42, 18646): 39.98386330354255, (42, 18653): 36.48981980367745, (42, 18654): 38.34524504374926, (42, 18655): 36.79343613698077, (42, 18666): 47.28483188125019, (42, 18837): 74.02997562487201, (42, 18974): 43.49054932291795, (42, 18999): 48.69931890299444, (42, 19000): 49.10036119257504, (42, 19174): 76.49727511283776, (42, 19342): 79.63455146321354, (42, 19455): 55.66039624724672, (42, 19555): 95.04805603473788, (42, 19564): 101.14289732871245, (42, 19573): 100.7407449883404, (42, 19586): 100.06818092066223, (42, 19605): 98.24535699792592, (42, 19611): 98.14200713644874, (42, 19614): 95.9964587966545, (42, 19641): 86.6310891304836, (42, 19702): 89.76228587115675, (42, 19713): 89.6003112335958, (42, 19731): 91.07496131013781, (42, 19819): 65.22754656027827, (42, 19893): 134.3587991534187, (42, 19899): 138.16410998067627, (42, 19929): 133.01228531362733, (42, 19951): 134.12839923894938, (42, 19962): 137.1187214393836, (42, 19970): 128.42114845768447, (42, 19971): 130.4159695762881, (42, 19972): 131.90752185542576, (42, 19975): 130.54726363318946, (42, 19978): 125.16554470148093, (42, 19987): 123.77790999812653, (42, 19989): 123.08858730500108, (42, 20039): 123.24079080433786, (42, 20043): 121.64149412330755, (42, 20047): 119.56390623786024, (42, 20052): 120.41579735690709, (42, 20054): 121.38497407135256, (42, 20085): 114.43386173422309, (42, 20104): 114.65368784343458, (42, 20132): 115.92240612464708, (42, 20203): 152.49332644715767, (42, 20280): 158.53074408940714, (42, 20285): 161.0459147942098, (42, 20290): 157.31281271381437, (42, 20297): 157.00680430318255, (42, 20309): 140.69731809202028, (42, 20453): 134.23814241565194, (42, 20485): 156.61471007815166, (42, 20520): 156.4578818326394, (42, 20526): 162.48661938565303, (42, 20698): 417.3703913171689, (42, 20868): 481.67244957501623, (42, 21042): 148.56189868132168, (42, 21057): 135.37966434484872, (42, 21066): 142.04056343535112, (42, 21075): 144.24307794348167, (42, 21093): 147.89029540977225, (42, 21098): 139.14423193494505, (42, 21127): 147.63231035304221, (42, 21130): 145.30898927107367, (42, 21144): 145.38234294072313, (42, 21146): 148.49411528841068, (42, 21147): 145.53285232361534, (42, 21148): 143.32730415176704, (42, 21153): 148.5438059696177, (42, 21293): 127.09412442773345, (42, 21426): 132.69749438299058, (42, 21442): 121.67558977808575, (42, 21451): 120.63045562978643, (42, 21466): 126.57510406413668, (42, 21469): 124.47874990327385, (42, 21471): 127.65735428444482, (42, 21473): 125.81767654607935, (42, 21475): 127.34565369306705, (42, 21482): 123.52222456091083, (42, 21484): 123.7625916764916, (42, 21488): 125.09180709952568, (42, 21494): 126.8863286699914, (42, 21498): 125.44050846096101, (42, 21500): 127.3844360735295, (42, 21514): 121.96276389549212, (42, 21537): 126.95353328675334, (42, 21662): 119.44607966136189, (42, 21691): 127.45653141763574, (42, 21757): 143.9377272820907, (42, 21777): 175.56883711537543, (42, 21778): 177.58232796841733, (42, 21779): 176.78637877471132, (42, 21790): 172.96607112543455, (42, 21802): 173.6999082894473, (42, 21824): 171.96623189334483, (42, 21874): 176.69985063191805, (42, 21879): 178.5893070158053, (42, 21983): 167.05697908896863, (42, 22002): 147.2491018816722, (42, 22132): 159.0667018920608, (42, 22261): 447.7292301128863, (42, 22298): 443.972238773883, (42, 22339): 469.213796242546, (42, 22508): 407.288699545964, (42, 22841): 853.4702117281608, (42, 22842): 853.5918786396447, (42, 22874): 849.0306884379903, (42, 22941): 849.1584726577738, (42, 22956): 852.2734041670332, (42, 22960): 852.8958739908761, (42, 22968): 857.3651031554381, (42, 22970): 857.9837231986847, (42, 22974): 860.3766430384151, (42, 22980): 864.0141156762318, (42, 23025): 864.8897609014015, (42, 23028): 864.3262347404524, (42, 23081): 871.8849078617048, (42, 23104): 867.1715151559729, (42, 23147): 831.860430430254, (42, 23298): 85.69562410421439, (42, 23376): 91.41361588052308, (42, 23381): 94.62648324171, (42, 23529): 81.56383669182084, (42, 23556): 84.94926926488617, (42, 23718): 90.21566345892329, (42, 24001): 53.30910922507337, (42, 24094): 39.97105330727936, (42, 24129): 34.26764040119134, (42, 24174): 46.379060943524784, (42, 24235): 34.03488365775908, (42, 24259): 27.832271491942382, (42, 24260): 28.307583740403043, (42, 24261): 29.504088199936753, (42, 24305): 24.0, (42, 24306): 24.0, (42, 24307): 24.0, (42, 24308): 46.67200605402781, (42, 24498): 24.0, (42, 24499): 24.0, (42, 24500): 24.0, (42, 24668): 33.56657990766557, (42, 24711): 24.0, (42, 24756): 24.0, (42, 24788): 24.0, (42, 24809): 24.0, (42, 24813): 24.0, (42, 24821): 24.0, (42, 24825): 24.0, (42, 24832): 24.0, (42, 24833): 24.0, (42, 24835): 24.0, (42, 24837): 24.0, (42, 24840): 24.0, (42, 24841): 24.0, (42, 24844): 24.0, (42, 24845): 24.0, (42, 24846): 24.0, (42, 24849): 24.0, (42, 24850): 24.0, (42, 24863): 24.0, (42, 24866): 24.0, (42, 24885): 24.0, (42, 24886): 24.0, (42, 24889): 24.0, (42, 24903): 24.0, (42, 24909): 24.0, (42, 24999): 84.40486536733718, (42, 25019): 84.51631316996236, (42, 25028): 82.80538930576375, (42, 25137): 182.95873040425877, (42, 25145): 181.78648498386693, (42, 25208): 194.32304874304495, (42, 25233): 196.137152317341, (42, 25371): 167.91130315606284, (42, 25377): 166.95171146463608, (42, 25828): 240.05448483682162, (42, 25851): 248.30010235147017, (42, 25874): 236.4926114041498, (42, 25898): 236.74206118271286, (42, 25946): 241.08588993753438, (42, 26047): 227.2778518293817, (42, 26066): 163.74914269925299, (42, 26197): 199.14069977730216, (42, 26212): 305.2862002958162, (42, 26253): 311.8233443210149, (42, 26254): 308.9306351410793, (42, 26257): 307.9363400685979, (42, 26258): 310.8835329533435, (42, 26260): 309.2707953476244, (42, 26266): 308.8550542450787, (42, 26267): 307.38423924432516, (42, 26271): 307.67524016206545, (42, 26304): 283.398821789031, (42, 26305): 282.6792384596425, (42, 26363): 252.11625783448284, (42, 26441): 457.96032512042484, (42, 26442): 457.3588453970715, (42, 26450): 454.0705003477704, (42, 26459): 453.52135885545266, (42, 26462): 453.85240173884006, (42, 26467): 463.4513230224727, (42, 26471): 460.90681046201627, (42, 26472): 460.66466575070285, (42, 26473): 460.59568937138386, (42, 26476): 459.4906775384041, (42, 26485): 455.29580162401186, (42, 26493): 455.5463661827958, (42, 26524): 455.1632189141352, (42, 26525): 454.8658182562157, (42, 26556): 459.59479378796686, (42, 26560): 459.0358697095213, (42, 26561): 456.9047841768199, (42, 26564): 458.77539159922276, (42, 26569): 456.47951013951916, (42, 26570): 455.74645448128035, (42, 26573): 456.4075361369282, (42, 26581): 456.45362622269073, (42, 26583): 455.6613081697457, (42, 26593): 456.63154919629545, (42, 26837): 464.2251283545925, (42, 26844): 466.36088940232173, (42, 26863): 462.01071726274176, (42, 26893): 468.27783032040907, (42, 26902): 471.18816439611, (42, 26905): 467.9754730085914, (42, 26912): 470.3321884217343, (42, 26921): 464.99414530251573, (42, 26922): 459.59769808594973, (42, 27212): 472.92594994668934, (42, 27218): 470.0228900586195, (42, 27239): 477.1860615437362, (42, 27257): 475.09015266589284, (42, 27274): 478.09114440899737, (42, 27279): 477.72214860461816, (42, 27282): 475.2411771215842, (42, 27283): 476.02809150226346, (42, 27285): 479.2738735101949, (42, 27286): 477.17299669575834, (42, 27290): 473.1368541135226, (42, 27295): 471.45973594951323, (42, 27300): 478.4800515346452, (42, 27344): 472.2869938190466, (42, 27366): 475.19182925922416, (42, 27383): 479.6972769276755, (42, 27398): 482.4835298596435, (42, 27406): 479.94388943743314, (42, 27407): 480.59775239124707, (42, 27426): 476.6733395505608, (42, 27432): 466.1417600510462, (42, 27460): 472.64612488403657, (42, 27523): 477.57792925127467, (42, 27545): 519.8213115851671, (42, 27602): 576.9910529082433, (42, 27606): 577.9113203197664, (42, 27646): 520.6292366525582, (42, 27667): 531.988958049809, (42, 27672): 532.511120788014, (42, 27674): 530.6203267811395, (42, 27688): 531.9520859757558, (42, 27692): 534.5600741520433, (42, 27693): 532.8748928722114, (42, 27705): 532.8691385095873, (42, 27712): 533.7681281667839, (42, 27786): 576.2902346618299, (42, 27790): 568.648176450335, (42, 27791): 567.927243074973, (42, 27795): 573.1979791335767, (42, 27801): 567.6217903368129, (42, 27813): 578.1833990272058, (42, 27816): 575.8655553690368, (42, 27823): 567.399022207289, (42, 27830): 573.0689403252296, (42, 27884): 502.5636001567943, (42, 27885): 515.9928227885847, (42, 27896): 507.82771449379413, (42, 27919): 507.18483860974845, (42, 27922): 508.97889502481706, (42, 27930): 504.49764747933096, (42, 27934): 505.08597176115035, (42, 27935): 505.5503339736824, (42, 27948): 574.8807277647308, (42, 27951): 576.8516206834939, (42, 28061): 528.0970565775336, (42, 28290): 645.1708881243101, (42, 28292): 647.596150514627, (42, 28293): 645.644757424764, (42, 28295): 644.6371425622921, (42, 28296): 645.0529955957588, (42, 28297): 643.8812093778942, (42, 28302): 643.0352508142754, (42, 28310): 678.108366353096, (42, 28313): 679.5531616482155, (42, 28372): 680.6470594266458, (42, 28398): 680.7825216398284, (42, 28399): 679.9525962546674, (42, 28400): 681.2005379159689, (42, 28401): 678.0194670673061, (42, 28445): 678.1547568648313, (42, 28475): 676.0267039927642, (42, 28885): 47.036117149198354, (42, 28886): 48.63727381938208, (42, 28915): 51.04029043521519, (42, 28916): 50.712615576643984, (42, 28917): 51.83624295045932, (42, 28921): 44.80047748903991, (42, 28931): 45.8438750743487, (42, 28945): 60.68551950347356, (42, 28982): 56.05056734630666, (42, 29219): 71.8889568871621, (42, 29228): 73.3574495002686, (42, 29246): 81.07812224168283, (42, 29248): 85.34696417695972, (42, 29282): 83.3859601211229, (42, 29290): 77.2994963362779, (42, 29291): 78.20353978698726, (42, 29292): 77.97486773057803, (42, 29293): 77.26422746469312, (42, 29294): 79.65159365103679, (42, 29298): 78.4530617308104, (42, 29299): 79.55199059678901, (42, 29304): 76.41674828578586, (42, 29317): 73.78935777079393, (42, 29323): 73.48083937353346, (42, 29330): 74.85236744483439, (42, 29331): 74.62355297407827, (42, 29344): 79.79382175619624, (42, 29445): 119.90956659590643, (42, 29724): 839.1909956824601, (42, 29738): 840.171703186389, (42, 29745): 837.0748541333702, (42, 29748): 836.4375324464612, (42, 29750): 837.5308838867337, (42, 29759): 835.2410842382066, (42, 29772): 838.8462908432303, (42, 29781): 838.0245212505749, (42, 29784): 837.9237587691983, (42, 29790): 838.5969125546277, (42, 29811): 836.0076079360929, (42, 29817): 839.4766946460499, (42, 29818): 838.6544600108726, (42, 29929): 837.4758428209491, (42, 30039): 853.4883159986247, (42, 30066): 847.0546275644493, (42, 30116): 811.2732929364162, (42, 30238): 758.351795746884, (42, 30248): 787.6971761686303, (42, 30260): 788.5705994340597, (42, 30545): 53.41404004387376, (42, 30733): 102.75293750344885, (42, 30756): 120.50191054008124, (42, 30921): 93.84848744302919, (42, 31079): 245.785461300471, (42, 31149): 244.37435647339333, (42, 31154): 245.38728836454953, (42, 31160): 244.57436576149047, (42, 31163): 246.08110868730972, (42, 31189): 262.6113666544191, (42, 31215): 262.4986268239494, (42, 31259): 269.4808776727843, (42, 31262): 270.96437036857816, (42, 31430): 248.2756252280642, (42, 31568): 305.67717258552585, (42, 31751): 257.8856183669887, (43, 109): 515.6672073019128, (43, 872): 24.0, (43, 873): 24.0, (43, 877): 24.0, (43, 879): 24.0, (43, 884): 24.0, (43, 889): 24.0, (43, 891): 24.0, (43, 892): 24.0, (43, 894): 24.0, (43, 896): 24.0, (43, 903): 24.0, (43, 909): 24.0, (43, 910): 24.0, (43, 912): 24.0, (43, 913): 24.0, (43, 916): 24.0, (43, 926): 24.0, (43, 927): 24.0, (43, 948): 24.0, (43, 961): 24.0, (43, 962): 24.0, (43, 963): 24.0, (43, 967): 24.0, (43, 974): 24.0, (43, 998): 24.0, (43, 1014): 55.89534671916599, (43, 1086): 36.34570276493127, (43, 1087): 40.551204339960876, (43, 1089): 39.51841307098599, (43, 1090): 38.673781068113605, (43, 1092): 37.075929964539405, (43, 1097): 37.47080578269857, (43, 1107): 39.00416722372219, (43, 1387): 399.0225309209971, (43, 1554): 432.7963150103023, (43, 1827): 126.1774518183779, (43, 1828): 126.16763004356471, (43, 1829): 126.74430150380904, (43, 1830): 127.6741847246646, (43, 1831): 127.66006015783263, (43, 1832): 127.25896929358197, (43, 1833): 127.06007277326772, (43, 1836): 126.51240268333373, (43, 1841): 128.4650872000367, (43, 1843): 127.78741862342055, (43, 1844): 128.31643133420476, (43, 1845): 127.71147933504169, (43, 1847): 124.42683000259018, (43, 1848): 125.40834403200154, (43, 1849): 130.23585505039438, (43, 1850): 130.50600430969666, (43, 1851): 126.77304350173443, (43, 1852): 127.38246339650905, (43, 1854): 127.4252628189392, (43, 1856): 124.99344872334729, (43, 1857): 125.63100788741147, (43, 1858): 129.4227016956394, (43, 1861): 127.13105569325502, (43, 1866): 125.39893673532923, (43, 1867): 128.0699144216193, (43, 1868): 127.10095299643935, (43, 1870): 128.9304694660882, (43, 1871): 127.5106111110668, (43, 1875): 127.01473069080437, (43, 1880): 125.12072134417909, (43, 1882): 126.17114472027947, (43, 1883): 129.94699665758623, (43, 1889): 124.74057666606294, (43, 1893): 125.95894080846462, (43, 1894): 125.16208004668763, (43, 1899): 123.8112489314978, (43, 1900): 124.11616035489045, (43, 1902): 127.09152015659187, (43, 1905): 128.26500873639563, (43, 1907): 125.50777709943466, (43, 1910): 125.17936087807963, (43, 1917): 128.41733271134777, (43, 1920): 125.11419481703152, (43, 1935): 127.41464633756607, (43, 1937): 128.29534584196622, (43, 1946): 121.21392447928041, (43, 1949): 121.74529808169304, (43, 1950): 120.27323380380408, (43, 1951): 121.25615728649164, (43, 1952): 123.5916173621785, (43, 1953): 122.77774216416822, (43, 1954): 123.06194956049977, (43, 1958): 122.06324524027596, (43, 1960): 123.71596219587816, (43, 1968): 124.36544172037628, (43, 1969): 126.62959037222241, (43, 1974): 126.11332734356226, (43, 1975): 126.4240091154586, (43, 1979): 123.9471841300811, (43, 1980): 124.76910609072122, (43, 1981): 124.69608512714056, (43, 1985): 124.87365172757255, (43, 1994): 121.63217143034416, (43, 2011): 126.50061026563863, (43, 2019): 134.42069331883664, (43, 2020): 133.3811531701345, (43, 2029): 130.4901530293893, (43, 2030): 132.64380024375234, (43, 2032): 130.57499829939752, (43, 2033): 131.56363950832807, (43, 2034): 132.0747159284233, (43, 2036): 131.34224216951122, (43, 2037): 131.42335259510514, (43, 2038): 129.1065154334849, (43, 2042): 139.39286135938693, (43, 2050): 130.32669602455334, (43, 2051): 130.75145004987382, (43, 2053): 130.7717693547603, (43, 2054): 131.70101506340842, (43, 2066): 129.9113344061858, (43, 2067): 129.62356342074744, (43, 2071): 119.64183754972413, (43, 2072): 120.89197004851131, (43, 2073): 114.8804825792699, (43, 2074): 115.00546606954435, (43, 2080): 113.10133874232639, (43, 2082): 121.69518160696592, (43, 2083): 122.31311098976536, (43, 2089): 120.11205756174355, (43, 2090): 120.5990889188454, (43, 2092): 119.21273492962689, (43, 2098): 113.44187631877976, (43, 2099): 114.72895903059197, (43, 2101): 113.76349968595932, (43, 2102): 117.5860777709922, (43, 2103): 116.57871251836787, (43, 2104): 116.26592904387942, (43, 2106): 123.1011526557399, (43, 2112): 114.73493302155516, (43, 2113): 118.43129406207223, (43, 2114): 120.20166375852567, (43, 2117): 124.1137029255253, (43, 2123): 103.30623279080278, (43, 2124): 104.18995975734936, (43, 2134): 102.31515997414677, (43, 2138): 104.64052207111143, (43, 2141): 102.41559862235059, (43, 2148): 106.64423939829369, (43, 2150): 100.40234645673517, (43, 2151): 101.5189538454141, (43, 2152): 100.09979665890924, (43, 2153): 106.61641711972261, (43, 2154): 102.85276053462024, (43, 2155): 103.02334748629784, (43, 2156): 101.9467911267704, (43, 2157): 105.0969582479187, (43, 2160): 107.14317447372623, (43, 2161): 100.22239348983298, (43, 2162): 108.07004662803068, (43, 2163): 106.75571235518747, (43, 2164): 106.89665024562737, (43, 2168): 102.22196821552525, (43, 2172): 104.52722464424649, (43, 2174): 101.75701654060012, (43, 2178): 105.69858173471012, (43, 2179): 105.2841043792845, (43, 2183): 104.87030915788638, (43, 2185): 105.08549788754031, (43, 2186): 104.29958213061128, (43, 2190): 107.0081012153429, (43, 2192): 105.6482963118061, (43, 2193): 105.02893252813372, (43, 2194): 103.6417392899131, (43, 2195): 103.78310406283056, (43, 2197): 106.12624996345458, (43, 2205): 104.72611999739551, (43, 2207): 102.82007848260322, (43, 2208): 103.96239460510311, (43, 2212): 104.73904238826826, (43, 2214): 85.00388349740356, (43, 2225): 89.87304171707713, (43, 2231): 73.52327466065545, (43, 2278): 106.9044577240055, (43, 2284): 110.65577128901494, (43, 2285): 110.74665031160686, (43, 2291): 108.81089101612939, (43, 2292): 105.47195227751638, (43, 2307): 109.03513982522377, (43, 2313): 109.49338521613322, (43, 2317): 102.0369156789607, (43, 2319): 106.74403153216987, (43, 2321): 108.57111669127308, (43, 2323): 107.360385711452, (43, 2326): 110.14583991535325, (43, 2327): 108.98240225607891, (43, 2329): 108.28986744399592, (43, 2330): 107.73631515694946, (43, 2332): 110.11089696874248, (43, 2344): 105.737202371838, (43, 2346): 106.36787326597566, (43, 2361): 100.61634183510542, (43, 2368): 117.27953220145562, (43, 2374): 119.0535078125335, (43, 2375): 119.1855633989158, (43, 2377): 114.17128971198242, (43, 2378): 120.27021617887445, (43, 2379): 121.00463403804861, (43, 2380): 121.01698715652712, (43, 2383): 115.02694402602141, (43, 2385): 115.5286990928935, (43, 2395): 115.0877382961808, (43, 2397): 120.74401894806988, (43, 2398): 112.64174032202405, (43, 2399): 114.02177794717821, (43, 2400): 113.63653963233808, (43, 2402): 117.99662936157512, (43, 2403): 119.07081756781588, (43, 2404): 119.09011026113788, (43, 2405): 116.7330229176001, (43, 2407): 118.28255425495564, (43, 2408): 119.80817612592384, (43, 2409): 117.34892838910358, (43, 2411): 120.12998239823688, (43, 2412): 119.4443732735487, (43, 2413): 120.47154581625938, (43, 2414): 119.18846743289218, (43, 2422): 120.1843790600281, (43, 2424): 119.51287168474053, (43, 2426): 119.52961031703136, (43, 2433): 117.95600625950811, (43, 2436): 118.13954892321186, (43, 2437): 111.73529098997498, (43, 2440): 112.94899555071119, (43, 2445): 146.43548465654118, (43, 2447): 142.42081298781514, (43, 2454): 145.54794297624332, (43, 2455): 145.1644530467926, (43, 2460): 136.21652711042307, (43, 2461): 137.44172388700227, (43, 2471): 159.89227102539738, (43, 2492): 167.2575486331062, (43, 2511): 153.53807902741065, (43, 2523): 160.66326726362703, (43, 2525): 161.05075319388902, (43, 2535): 147.72434103973552, (43, 2537): 146.2087869671657, (43, 2538): 146.54679636522675, (43, 2539): 149.51270590837373, (43, 2540): 148.504946046204, (43, 2542): 150.82560955851807, (43, 2559): 171.91481990275275, (43, 2575): 172.94675685023034, (43, 2599): 122.05685935052381, (43, 2600): 133.5301274337804, (43, 2607): 124.45329394063562, (43, 2627): 172.7062682762782, (43, 2647): 180.23190871671008, (43, 2674): 173.41071407070214, (43, 2681): 174.85824064939263, (43, 2683): 176.2445764173355, (43, 2686): 172.53099696292063, (43, 2689): 206.5887851496814, (43, 2690): 207.2208480885251, (43, 2713): 227.9954691823131, (43, 2714): 230.55504723886503, (43, 2715): 231.24431672907846, (43, 2739): 230.0369772209977, (43, 2740): 220.05996851835235, (43, 2741): 220.01117971962907, (43, 2749): 231.22198046282432, (43, 2750): 230.7152987954129, (43, 2752): 230.87990150040324, (43, 2755): 231.88202305985953, (43, 2758): 232.32823498353534, (43, 2759): 232.00647870197935, (43, 2769): 230.37993290707544, (43, 2771): 222.6442134458772, (43, 2779): 228.10125015712356, (43, 2784): 222.6536480403033, (43, 2800): 229.40753672490573, (43, 2802): 221.48308469799167, (43, 2803): 220.5581211591157, (43, 2804): 219.8265151206218, (43, 2805): 224.06634509579973, (43, 2807): 223.35384394482, (43, 2809): 224.58685789615697, (43, 2812): 218.3898210124623, (43, 2814): 228.825215919576, (43, 2817): 235.11165754354653, (43, 2819): 221.8162009292271, (43, 2823): 224.71131807349647, (43, 2832): 225.88972527602473, (43, 2836): 222.62775071533687, (43, 2839): 222.66708295245357, (43, 2841): 232.14561731697682, (43, 2843): 230.81385544909264, (43, 2846): 225.99830885231503, (43, 2849): 227.5299779266131, (43, 2852): 226.35897203933135, (43, 2853): 228.11035627020223, (43, 2876): 231.57547529361563, (43, 2877): 234.6490643885252, (43, 2885): 241.86424963441976, (43, 2918): 217.9804058286335, (43, 2921): 219.9182560730245, (43, 2925): 208.72828672415253, (43, 2926): 203.80701346325185, (43, 2930): 218.32130071473517, (43, 2931): 211.02076095015133, (43, 2938): 219.1326817843794, (43, 2940): 217.25214485745326, (43, 2947): 211.81001802990556, (43, 2949): 215.694673173393, (43, 2950): 217.34014367323604, (43, 2952): 216.7989159804802, (43, 2958): 216.22333380935808, (43, 2959): 215.4801210689857, (43, 2960): 217.2000352148844, (43, 2961): 217.09437165727476, (43, 2963): 216.39036977304843, (43, 2968): 217.42679312596493, (43, 2976): 215.5529053050216, (43, 2981): 213.3984231300726, (43, 2982): 214.5342993170307, (43, 2984): 214.34678138871314, (43, 3003): 215.03358260345485, (43, 3046): 192.01900492316352, (43, 3050): 205.02104441035124, (43, 3051): 204.89731728085587, (43, 3053): 204.3395892033408, (43, 3069): 213.12902352646748, (43, 3071): 200.84132124367986, (43, 3080): 244.2197681730253, (43, 3199): 222.30051687588025, (43, 3200): 222.19281518284572, (43, 3205): 228.2491249244795, (43, 3209): 222.93539068387102, (43, 3215): 221.44356227708337, (43, 3217): 220.31773972622406, (43, 3249): 220.68880810838814, (43, 3263): 229.205207746027, (43, 3289): 221.15248429900845, (43, 3301): 223.52284794831624, (43, 3302): 222.3324234721944, (43, 3307): 221.5884872230689, (43, 3310): 224.0271601311695, (43, 3391): 266.38165403351, (43, 3509): 208.60801126290565, (43, 3510): 209.68813743767384, (43, 3511): 208.3273452775253, (43, 3512): 208.44443260594986, (43, 3514): 207.71585784125773, (43, 3519): 209.35710442180138, (43, 3536): 205.5681033948104, (43, 3545): 203.2194056087766, (43, 3548): 204.04888933469533, (43, 3572): 205.7448652331914, (43, 3581): 209.23313474335907, (43, 3583): 207.2796281953272, (43, 3601): 208.4747713214119, (43, 3656): 212.81601416605557, (43, 3669): 220.70017662016372, (43, 3670): 220.07963438188767, (43, 3695): 222.70299642011756, (43, 3696): 221.88374285832356, (43, 3782): 193.4934376951272, (43, 3792): 196.21198364237648, (43, 3989): 777.2609371140553, (43, 4008): 784.7514423562665, (43, 4031): 784.2046516661695, (43, 4045): 781.6047470822256, (43, 4144): 782.0513194332384, (43, 4145): 774.5438418595044, (43, 4164): 779.163048371603, (43, 4168): 776.8336919692944, (43, 4173): 776.3588691699821, (43, 4181): 771.784467784952, (43, 4228): 767.4426254550453, (43, 4248): 765.5810080577672, (43, 4254): 723.9428272687295, (43, 4260): 724.1790457035563, (43, 4262): 726.7954172840266, (43, 4273): 726.266711329817, (43, 4319): 700.2856071349975, (43, 4326): 699.4754135426107, (43, 4328): 699.8511365302985, (43, 4334): 701.3248420617068, (43, 4335): 700.6820597857505, (43, 4372): 632.3734299043682, (43, 4413): 651.3037824536136, (43, 4434): 632.0633375646786, (43, 4447): 636.5141819052664, (43, 4452): 632.0840921692346, (43, 4463): 578.1167070890658, (43, 4465): 580.2738885113744, (43, 4619): 648.2348173380104, (43, 4645): 654.2753171387177, (43, 4657): 652.7511030919212, (43, 4666): 650.1061331953588, (43, 4676): 653.7411416439792, (43, 4678): 654.8883227702137, (43, 4689): 651.5672675628105, (43, 4704): 669.5005828390317, (43, 4726): 697.3766566645053, (43, 4727): 696.7885822191664, (43, 4730): 695.7019940839167, (43, 4731): 695.6619923546064, (43, 4734): 698.315305209478, (43, 4735): 697.4556983046692, (43, 4736): 697.4737654787261, (43, 4737): 696.12792263723, (43, 4738): 696.0473165641118, (43, 4756): 696.4736698748637, (43, 4760): 695.0105446439414, (43, 4761): 695.9396398363358, (43, 4762): 693.8457756558693, (43, 4765): 695.1210895439224, (43, 4773): 698.8296085684754, (43, 4774): 697.7962101471129, (43, 4790): 698.514460548223, (43, 4795): 698.1275171093741, (43, 4799): 697.7818683650047, (43, 4801): 698.3216805345893, (43, 4804): 698.9633711938758, (43, 4805): 698.6381070715111, (43, 4806): 696.8236669453574, (43, 4815): 695.8123446909198, (43, 4816): 697.5194365002552, (43, 4817): 697.2271708091986, (43, 4826): 696.5273159358858, (43, 4830): 695.4405679471395, (43, 4839): 696.6922504564544, (43, 4840): 696.9661190399671, (43, 4841): 695.5240354747001, (43, 4846): 695.2156542788678, (43, 4848): 694.577444343333, (43, 4850): 695.0253754886145, (43, 4871): 690.5358348359025, (43, 4883): 695.0843539682619, (43, 4900): 693.452842198476, (43, 4901): 692.320969387357, (43, 4917): 637.9756175597956, (43, 4931): 633.1422515212756, (43, 4944): 638.9091535217149, (43, 4956): 633.642854377275, (43, 4958): 632.7411160219318, (43, 4959): 631.3013934903105, (43, 4961): 634.9326063121359, (43, 4966): 632.0202863713131, (43, 5207): 626.5923156448912, (43, 5272): 562.6550713602785, (43, 5283): 564.0343313812793, (43, 5287): 564.3511723110506, (43, 5289): 564.8897991954979, (43, 5293): 564.7701491147443, (43, 5295): 568.9029593842431, (43, 5296): 567.7191036163999, (43, 5298): 567.0262461860357, (43, 5303): 567.2668978634446, (43, 5305): 559.5502599519299, (43, 5306): 556.7596634802966, (43, 5307): 558.6899034939534, (43, 5308): 559.8469797784468, (43, 5313): 561.2496987737995, (43, 5314): 562.6142181360451, (43, 5317): 559.0982920109919, (43, 5319): 565.5573590885812, (43, 5324): 565.604044311501, (43, 5326): 565.703322244484, (43, 5348): 555.4165839155237, (43, 5351): 554.8756061199969, (43, 5399): 564.04580215109, (43, 5413): 554.1939000376075, (43, 5422): 565.9967290097383, (43, 5445): 562.0709861519277, (43, 5448): 560.6330105892329, (43, 5456): 559.0678757099095, (43, 5467): 560.0795613657837, (43, 5624): 548.3961597035766, (43, 5671): 610.5706722694471, (43, 5672): 608.7142310814339, (43, 5797): 633.8868413000571, (43, 5871): 574.0458457104569, (43, 5976): 556.0008983595161, (43, 6118): 224.9522090163476, (43, 6248): 261.61938203968515, (43, 6345): 508.9753749602209, (43, 6352): 503.74820902356487, (43, 6354): 509.99315362492837, (43, 6359): 511.5006142698524, (43, 6376): 505.76288303519175, (43, 6378): 509.42449312148057, (43, 6381): 511.4003440420111, (43, 6383): 507.67384279440256, (43, 6396): 512.7120850731853, (43, 6399): 509.61577130124425, (43, 6408): 503.4535319271936, (43, 6409): 504.66669291271637, (43, 6419): 494.2185160417157, (43, 6422): 503.1478799793708, (43, 6423): 502.65431920345446, (43, 6424): 508.09369877242443, (43, 6439): 506.6869953285635, (43, 6464): 504.8417737651389, (43, 6465): 504.7326454566069, (43, 6469): 506.28471671549346, (43, 6470): 506.17025414582275, (43, 6472): 513.4645609342901, (43, 6480): 510.34312552759036, (43, 6486): 511.46035509147544, (43, 6497): 510.97201681200187, (43, 6503): 502.8259138073432, (43, 6508): 504.4671081239086, (43, 6509): 504.9242968314187, (43, 6521): 510.1239497984455, (43, 6544): 508.5533778107565, (43, 6552): 501.89124505158367, (43, 6553): 500.9344287535217, (43, 6554): 499.9775752292729, (43, 6578): 503.6700614571074, (43, 6582): 501.7127052313009, (43, 6601): 503.83350536781836, (43, 6609): 512.5793892853542, (43, 6610): 512.5713062446736, (43, 6611): 513.4496429469733, (43, 6614): 513.393804029974, (43, 6615): 513.3168937389456, (43, 6616): 513.3640710739103, (43, 6617): 513.2633039873618, (43, 6618): 513.7034449558339, (43, 6619): 512.5893466631628, (43, 6620): 512.955013258435, (43, 6621): 512.0894295400183, (43, 6622): 512.5682831694354, (43, 6623): 512.8343166392827, (43, 6624): 511.6881397437281, (43, 6625): 511.7762693164643, (43, 6626): 512.7374312364018, (43, 6627): 513.5867949161862, (43, 6628): 512.359357951534, (43, 6629): 511.3742281406034, (43, 6630): 511.80929020880683, (43, 6632): 511.5336605896858, (43, 6634): 510.6903781779316, (43, 6635): 512.0413165239993, (43, 6636): 513.2590099180533, (43, 6637): 510.2584265701498, (43, 6638): 511.4872267047872, (43, 6639): 513.410497793254, (43, 6640): 511.8389236744627, (43, 6641): 511.73533500464043, (43, 6642): 511.2150174078736, (43, 6643): 512.9627675652283, (43, 6645): 512.499281926105, (43, 6646): 513.7595455937981, (43, 6647): 511.6100364925731, (43, 6653): 513.4162825060646, (43, 6655): 513.5620032644108, (43, 6658): 510.4616520184504, (43, 6662): 510.85974634259975, (43, 6819): 460.63097612236584, (43, 6996): 469.9009055255137, (43, 7059): 480.7978334640254, (43, 7187): 451.61034377977353, (43, 7304): 434.04628085628747, (43, 7528): 464.0600238957787, (43, 7720): 533.0092238492741, (43, 7793): 530.0535724544435, (43, 7807): 531.4684456483008, (43, 7808): 529.3663036985787, (43, 7831): 515.4090156645835, (43, 7850): 527.5778223088492, (43, 7852): 525.8289143536393, (43, 8012): 532.3131554884563, (43, 8125): 531.14895021197, (43, 8208): 552.9176441801327, (43, 8392): 517.3776732940125, (43, 8651): 409.4184150821158, (43, 9088): 466.14981914463914, (43, 9443): 363.68291254603713, (43, 9444): 365.01086888713627, (43, 9828): 308.45176754240873, (43, 9868): 313.6204234270596, (43, 10180): 531.6232336550628, (43, 10256): 559.6414995974434, (43, 10276): 547.7751758864125, (43, 10378): 555.0628484844718, (43, 10676): 517.0409626055005, (43, 10714): 496.97408236317506, (43, 10730): 504.090204118677, (43, 10862): 461.23762287098145, (43, 10881): 465.7004309552239, (43, 10883): 464.9862152179321, (43, 10885): 460.3344551578022, (43, 10891): 463.8781000723362, (43, 10909): 464.00780805899, (43, 10911): 465.171927354873, (43, 10913): 463.9681747948135, (43, 10915): 464.20003318111435, (43, 10919): 465.05458170616356, (43, 11037): 428.5846369425736, (43, 11039): 419.6790084931487, (43, 11516): 855.0102163417947, (43, 11856): 702.0306924652449, (43, 11857): 700.509780724274, (43, 11861): 701.3011763409155, (43, 11881): 700.6251732050362, (43, 11902): 695.5783249169126, (43, 11911): 695.0921665021258, (43, 11914): 695.607011633258, (43, 11922): 699.2085938517267, (43, 11924): 700.5080189559848, (43, 11926): 699.0795271169497, (43, 11950): 702.4131500527116, (43, 11963): 707.096102181744, (43, 11983): 704.5987918049458, (43, 11985): 709.4084516015156, (43, 12009): 709.0893880609487, (43, 12010): 705.6167358479751, (43, 12018): 706.245750422841, (43, 12020): 707.0632244682803, (43, 12021): 707.6803393036297, (43, 12024): 710.8634648760253, (43, 12025): 709.6654378702857, (43, 12027): 708.9419568697932, (43, 12031): 705.056238642314, (43, 12032): 706.0690056207578, (43, 12035): 709.0138574587808, (43, 12041): 709.4513330991258, (43, 12045): 665.8003852199441, (43, 12145): 686.8420957445394, (43, 12275): 780.5138296393108, (43, 12294): 772.4028659802999, (43, 12358): 799.4272153010403, (43, 12463): 810.2178248309841, (43, 12465): 809.9403868317282, (43, 12482): 814.002424392963, (43, 12503): 813.4884480609498, (43, 12506): 814.7032166366747, (43, 12549): 811.5306945837383, (43, 12559): 810.713776945665, (43, 12569): 811.902177019997, (43, 12572): 812.8042114247047, (43, 12574): 810.8591795373392, (43, 12576): 812.5193338370702, (43, 12591): 811.9822874639278, (43, 12608): 819.1024057966679, (43, 12696): 807.1020554100755, (43, 12710): 813.555189294011, (43, 12728): 810.6638625960757, (43, 12766): 610.3296131207737, (43, 12771): 599.5941252419569, (43, 12790): 598.4144018766565, (43, 12795): 595.899219342968, (43, 12797): 583.01290959533, (43, 12798): 584.5917249060212, (43, 12811): 594.2166909438762, (43, 12830): 591.2836334825406, (43, 12848): 592.3707734729604, (43, 12850): 592.8289369677705, (43, 12852): 590.6493866001998, (43, 12854): 589.1786180964071, (43, 12859): 593.6804409310417, (43, 12861): 586.0878143065105, (43, 12865): 596.2817100514357, (43, 12866): 595.3511163388516, (43, 12867): 598.4527786394164, (43, 12874): 596.9726245731796, (43, 12875): 598.0106080844117, (43, 12881): 593.6492095958326, (43, 12883): 595.446862242626, (43, 12885): 599.01559389068, (43, 12888): 594.4890737000923, (43, 12889): 593.9645883406648, (43, 12892): 597.3550305986205, (43, 12893): 594.6760042413839, (43, 12896): 595.4298470384675, (43, 12906): 597.6085938619445, (43, 13018): 587.9469611096811, (43, 13071): 588.9278189090924, (43, 13131): 574.0538455510872, (43, 13146): 582.9639499076592, (43, 13159): 574.1051863511033, (43, 13193): 571.9596868806224, (43, 13198): 553.8264619619002, (43, 13292): 572.7206521262497, (43, 13296): 576.8475871168523, (43, 13406): 545.8518025138087, (43, 13407): 545.5128509089836, (43, 13417): 545.9399789085637, (43, 13418): 548.0098329886207, (43, 13438): 553.9554801508871, (43, 13442): 554.8521547140233, (43, 13443): 553.5233556847884, (43, 13764): 453.38729575401675, (43, 13766): 454.99303500570505, (43, 13771): 454.6002996183458, (43, 13783): 450.10467299359465, (43, 13784): 456.24622095539536, (43, 13792): 453.319502850934, (43, 13824): 449.2302613921316, (43, 14017): 452.3710347162842, (43, 14870): 472.72527555104284, (43, 14997): 442.68562896220527, (43, 15000): 442.7026329111886, (43, 15003): 443.75536906357684, (43, 15006): 447.16756511943714, (43, 15007): 448.362748014341, (43, 15056): 447.71236106859135, (43, 15063): 446.535124200289, (43, 15069): 445.96126943433404, (43, 15076): 448.43229509147847, (43, 15086): 444.8495716885585, (43, 15087): 443.2894505272147, (43, 15111): 439.8302452293709, (43, 15116): 441.7958020477353, (43, 15722): 409.94881145027557, (43, 15998): 384.26346385406174, (43, 16073): 308.4847697501467, (43, 16939): 87.58451866719751, (43, 16940): 86.19544866250537, (43, 16951): 91.20642890946486, (43, 16963): 90.49147993623464, (43, 16965): 90.7018488777459, (43, 16969): 92.4257453576618, (43, 16970): 89.89695309419363, (43, 16971): 89.60580726641486, (43, 16973): 90.82956507042705, (43, 16974): 91.97205473848376, (43, 16976): 89.14350216412431, (43, 16978): 88.48669980606356, (43, 16980): 88.22485510722159, (43, 16982): 93.24555141462248, (43, 17045): 211.3718280799173, (43, 17048): 212.86800233971374, (43, 17304): 754.6602534603572, (43, 17305): 753.5340228566693, (43, 17330): 754.695838811681, (43, 17334): 752.1631451356578, (43, 17343): 756.5765110610488, (43, 17345): 752.2220324093895, (43, 17347): 754.6191757449318, (43, 17351): 748.8070633287786, (43, 17372): 751.9449421382625, (43, 17373): 756.4089567661633, (43, 17377): 756.7343205320199, (43, 17382): 753.8590755620918, (43, 17383): 754.3440303607115, (43, 17389): 752.658791340322, (43, 17400): 755.5617767865496, (43, 17401): 755.4807105174956, (43, 17402): 755.7462070134405, (43, 17403): 756.0449133039376, (43, 17440): 752.5518418194603, (43, 17455): 756.1681037878158, (43, 17491): 756.5451790893497, (43, 17507): 750.0645272358889, (43, 17509): 751.6167671286117, (43, 17590): 747.9048480077229, (43, 17615): 737.9876853852895, (43, 17642): 739.6795954749398, (43, 17643): 739.6089419644373, (43, 17668): 737.8789714523319, (43, 17721): 733.701478197093, (43, 17754): 748.6431698297948, (43, 17769): 750.3999426599064, (43, 17776): 744.351702206133, (43, 17804): 752.9616804803194, (43, 17809): 754.5630274935039, (43, 17824): 753.4086160455129, (43, 17837): 749.2591720144598, (43, 17838): 749.5202125961902, (43, 17862): 748.3707442715768, (43, 17866): 751.7362536016317, (43, 17872): 747.1700372684742, (43, 17873): 744.6183003638732, (43, 17881): 748.546156671758, (43, 17947): 115.32902784742723, (43, 17951): 118.65657341804571, (43, 17953): 119.36021181426561, (43, 17954): 119.17735367979549, (43, 17959): 115.8957591210998, (43, 17963): 117.01679431709361, (43, 18000): 134.49539707057167, (43, 18001): 133.77848182149344, (43, 18111): 111.47868064342833, (43, 18148): 180.33141914673678, (43, 18166): 153.90504883379882, (43, 18189): 125.85681666750756, (43, 18239): 757.1671562210762, (43, 18240): 757.1554106157191, (43, 18245): 757.3207867540455, (43, 18247): 756.9778402750125, (43, 18251): 757.3236108865051, (43, 18256): 757.706736476326, (43, 18258): 757.3085986835962, (43, 18259): 757.3848215233157, (43, 18260): 757.5462167368854, (43, 18262): 757.8479237557299, (43, 18263): 757.8162643327105, (43, 18264): 757.9763732184837, (43, 18266): 757.9732109786981, (43, 18267): 758.1287998051345, (43, 18268): 758.2077781343456, (43, 18269): 758.5184592709355, (43, 18275): 758.3719237433115, (43, 18285): 757.9191721395781, (43, 18308): 754.6412772061797, (43, 18313): 753.5507446809557, (43, 18314): 754.073278244494, (43, 18315): 758.484181721859, (43, 18316): 758.4675878271579, (43, 18317): 758.613485862633, (43, 18320): 758.7380404898264, (43, 18321): 758.8222648382881, (43, 18322): 759.0503552744026, (43, 18324): 759.2236559972142, (43, 18325): 759.920894932473, (43, 18326): 759.6607193082181, (43, 18327): 758.7542999461037, (43, 18329): 760.2240741307705, (43, 18330): 759.9028600470959, (43, 18331): 759.4320110431997, (43, 18332): 758.9514763475458, (43, 18333): 759.8224842457776, (43, 18336): 759.4179696818959, (43, 18337): 759.6490961800997, (43, 18403): 759.3444773233734, (43, 18432): 750.0224715742515, (43, 18451): 756.3551478150114, (43, 18466): 762.4341110030468, (43, 18481): 758.6401932396589, (43, 18483): 758.6472532922616, (43, 18484): 758.2578623533483, (43, 18485): 757.0767165450176, (43, 18486): 758.0758140641218, (43, 18487): 757.171958168542, (43, 18489): 757.9977380783015, (43, 18490): 758.8656932019693, (43, 18491): 759.2859795219427, (43, 18492): 756.2813260583135, (43, 18493): 757.9156051313107, (43, 18494): 757.8337217428258, (43, 18495): 758.5511810911996, (43, 18496): 758.1178600664938, (43, 18497): 756.9551150253235, (43, 18498): 757.1974216525624, (43, 18499): 757.8554172214855, (43, 18501): 757.3632467662213, (43, 18502): 756.9410716171848, (43, 18503): 756.6283550855276, (43, 18504): 758.3026295976942, (43, 18506): 757.3991701318005, (43, 18507): 756.9908829564662, (43, 18508): 757.7550763525973, (43, 18509): 757.7548402240444, (43, 18510): 756.6261209551859, (43, 18511): 758.0232702794815, (43, 18512): 757.5441197765168, (43, 18515): 758.3298587059171, (43, 18516): 758.3325132414265, (43, 18517): 757.7853013156246, (43, 18518): 758.6883006737881, (43, 18519): 758.3986580700246, (43, 18520): 757.6414603754698, (43, 18522): 760.2014317991142, (43, 18523): 760.2830228194664, (43, 18532): 760.852078194586, (43, 18535): 759.6598281461687, (43, 18537): 758.9959452961918, (43, 18539): 759.1296183932435, (43, 18540): 759.2013912955429, (43, 18541): 759.5235491031801, (43, 18542): 759.7290259844573, (43, 18543): 758.7040241421984, (43, 18546): 759.1734794021737, (43, 18555): 760.2128690805813, (43, 18556): 760.3946692160345, (43, 18565): 760.7609344297248, (43, 18567): 761.0435353269004, (43, 18568): 760.4858925674132, (43, 18577): 764.5556119637861, (43, 18583): 763.9032049174044, (43, 18605): 764.7945879583069, (43, 18608): 761.3480431695914, (43, 18616): 768.5924058489605, (43, 18618): 771.8024319342366, (43, 18625): 770.7810688375093, (43, 18645): 767.953577886161, (43, 18646): 768.6741592683846, (43, 18653): 765.8967620230442, (43, 18654): 768.4960966228797, (43, 18655): 766.7704654897326, (43, 18666): 777.4198253539853, (43, 18837): 766.5058067877034, (43, 18974): 756.4857857999258, (43, 18999): 759.3134132165748, (43, 19000): 760.2997478214129, (43, 19174): 714.2156255554386, (43, 19342): 734.5687980201618, (43, 19455): 720.8935986944103, (43, 19555): 673.1993781003482, (43, 19564): 677.1623673682833, (43, 19573): 674.8297543432298, (43, 19586): 673.7202140606814, (43, 19605): 674.3415994504895, (43, 19611): 675.8783472221781, (43, 19614): 674.8931973779592, (43, 19641): 699.2872631639796, (43, 19702): 699.1819389714527, (43, 19713): 697.3316328558344, (43, 19731): 663.5507088674636, (43, 19819): 714.0401564264313, (43, 19893): 639.4626240651186, (43, 19899): 648.2873678967909, (43, 19929): 642.3147295786378, (43, 19951): 661.831655154718, (43, 19962): 642.8844670468196, (43, 19970): 649.2505274290289, (43, 19971): 648.8605927832182, (43, 19972): 646.8628119294531, (43, 19975): 646.4242705711239, (43, 19978): 668.1805530805427, (43, 19987): 668.848633846302, (43, 19989): 663.4250405320741, (43, 20039): 670.0075949608657, (43, 20043): 672.7346905672713, (43, 20047): 671.4004914601946, (43, 20052): 665.0244196458141, (43, 20054): 665.2806800113067, (43, 20085): 695.6780687145009, (43, 20104): 697.4960608772847, (43, 20132): 685.9089644361333, (43, 20203): 633.886456103793, (43, 20280): 630.1732356098634, (43, 20285): 628.9833975144907, (43, 20290): 631.4214666992673, (43, 20297): 629.6734076525856, (43, 20309): 666.1008964218148, (43, 20453): 698.180663904475, (43, 20485): 618.5442416023631, (43, 20520): 614.197329539793, (43, 20526): 610.8737611941339, (43, 20698): 432.5864360713119, (43, 20868): 388.0150096458667, (43, 21042): 586.1662890658895, (43, 21057): 599.4535380025959, (43, 21066): 592.5204387043045, (43, 21075): 590.6306118485251, (43, 21093): 586.5798103398115, (43, 21098): 595.1612332087875, (43, 21127): 586.9470302876113, (43, 21130): 589.1655487129528, (43, 21144): 589.341645109591, (43, 21146): 586.0824877508192, (43, 21147): 589.2860558699067, (43, 21148): 591.3935180216753, (43, 21153): 588.0951084000415, (43, 21293): 607.386083974521, (43, 21426): 609.3390780729754, (43, 21442): 624.3471351485199, (43, 21451): 625.7686419096883, (43, 21466): 616.5261646242778, (43, 21469): 618.4919122253526, (43, 21471): 615.5407854645831, (43, 21473): 617.1017986137311, (43, 21475): 615.634744605477, (43, 21482): 619.9448903894568, (43, 21484): 619.4243087785236, (43, 21488): 618.3293392182272, (43, 21494): 615.3279684978562, (43, 21498): 616.8684679306122, (43, 21500): 614.1978030043182, (43, 21514): 617.2010353918141, (43, 21537): 613.1085739028995, (43, 21662): 618.259680332866, (43, 21691): 610.2704761675217, (43, 21757): 598.2920298986537, (43, 21777): 558.7476481341278, (43, 21778): 556.7299273220054, (43, 21779): 557.5667814564573, (43, 21790): 561.333575173286, (43, 21802): 560.659454051117, (43, 21824): 562.4708550037371, (43, 21874): 557.7351369203548, (43, 21879): 556.0157748531124, (43, 21983): 567.4598197644804, (43, 22002): 587.2692942830037, (43, 22132): 580.3116668438178, (43, 22261): 292.88725134371657, (43, 22298): 297.7131475920826, (43, 22339): 276.9527720897916, (43, 22508): 332.23856382157595, (43, 22841): 357.6140912013058, (43, 22842): 356.7515241437889, (43, 22874): 351.0728166991564, (43, 22941): 354.31130327934494, (43, 22956): 355.20443492873545, (43, 22960): 357.77631363796905, (43, 22968): 347.5606965300245, (43, 22970): 349.7296325067634, (43, 22974): 343.11587991446055, (43, 22980): 345.09248015596853, (43, 23025): 334.2124566723952, (43, 23028): 331.55842369020843, (43, 23081): 321.8365670383466, (43, 23104): 300.0118122806981, (43, 23147): 313.536730409995, (43, 23298): 650.7907980724026, (43, 23376): 644.888591998259, (43, 23381): 640.1656550844059, (43, 23529): 653.5898265442166, (43, 23556): 650.3278404786042, (43, 23718): 648.1532807726426, (43, 24001): 685.9378483764917, (43, 24094): 694.9510442249594, (43, 24129): 700.7969254587788, (43, 24174): 687.9224295123395, (43, 24235): 700.4277172480664, (43, 24259): 706.4827822864683, (43, 24260): 705.9924728821599, (43, 24261): 704.8077139380879, (43, 24305): 713.3406064885983, (43, 24306): 714.3738185760038, (43, 24307): 712.7287225065058, (43, 24308): 701.6713635353922, (43, 24498): 729.4242139496388, (43, 24499): 729.5198515132352, (43, 24500): 728.4771498614886, (43, 24668): 722.8443511163334, (43, 24711): 736.0049600360246, (43, 24756): 739.4008768878133, (43, 24788): 741.2735022308807, (43, 24809): 734.3255335419992, (43, 24813): 736.5317919809846, (43, 24821): 735.8233940816217, (43, 24825): 736.2782382415068, (43, 24832): 733.9106983595462, (43, 24833): 734.9307742894617, (43, 24835): 735.9257533864778, (43, 24837): 737.5975328801264, (43, 24840): 733.7276040517415, (43, 24841): 735.3557203631898, (43, 24844): 733.7400520166927, (43, 24845): 734.801705261108, (43, 24846): 734.526951953425, (43, 24849): 735.0666593950018, (43, 24850): 736.8020667533502, (43, 24863): 722.8576094985362, (43, 24866): 724.6940410682071, (43, 24885): 726.7436587022588, (43, 24886): 726.8286655821177, (43, 24889): 731.0836730093919, (43, 24903): 732.740064771363, (43, 24909): 726.2609635852865, (43, 24999): 805.4303858730395, (43, 25019): 803.5118736016556, (43, 25028): 804.3261662144276, (43, 25137): 628.2466963737565, (43, 25145): 630.5517053928878, (43, 25208): 652.0737765113704, (43, 25233): 648.8040753701013, (43, 25371): 631.7079151495188, (43, 25377): 626.2064649187461, (43, 25828): 513.1615179559998, (43, 25851): 498.1706716445541, (43, 25874): 513.7655231454819, (43, 25898): 519.0871735638817, (43, 25946): 511.5340890340308, (43, 26047): 543.7471339798202, (43, 26066): 593.5668101637519, (43, 26197): 562.9187770295293, (43, 26212): 451.4428157383708, (43, 26253): 445.29400122499516, (43, 26254): 447.6868902984793, (43, 26257): 449.67935885542533, (43, 26258): 446.4840759123103, (43, 26260): 448.1385772635462, (43, 26266): 446.15804582285267, (43, 26267): 448.0596096185436, (43, 26271): 448.080755155403, (43, 26304): 469.9953727185593, (43, 26305): 469.94692979299776, (43, 26363): 505.1823459707527, (43, 26441): 310.3414540444169, (43, 26442): 310.3175307169825, (43, 26450): 313.2237554479659, (43, 26459): 315.9207361705669, (43, 26462): 316.6301745766889, (43, 26467): 308.6833644611267, (43, 26471): 309.60685785352945, (43, 26472): 309.4672967354613, (43, 26473): 309.19663032358164, (43, 26476): 306.8208725721879, (43, 26485): 313.31473040915915, (43, 26493): 311.95765981136196, (43, 26524): 316.567804005563, (43, 26525): 316.18318706417296, (43, 26556): 310.80855542227886, (43, 26560): 313.2098385817355, (43, 26561): 315.42099420557486, (43, 26564): 310.96882942161955, (43, 26569): 315.1315935558153, (43, 26570): 315.0056961512799, (43, 26573): 313.4375358060417, (43, 26581): 312.5033221117171, (43, 26583): 313.7204397446754, (43, 26593): 311.2325050675728, (43, 26837): 307.0979706197097, (43, 26844): 305.773373083032, (43, 26863): 306.21419747896107, (43, 26893): 301.2882949015039, (43, 26902): 299.37813254530744, (43, 26905): 303.55642672252014, (43, 26912): 301.3633792955681, (43, 26921): 304.00078033940093, (43, 26922): 304.5493388236774, (43, 27212): 358.4107526680053, (43, 27218): 362.545243195757, (43, 27239): 355.796275292998, (43, 27257): 355.81971940548846, (43, 27274): 354.8151745971911, (43, 27279): 353.9104080849326, (43, 27282): 355.1616233727638, (43, 27283): 356.8394556291026, (43, 27285): 353.58251648636883, (43, 27286): 352.76775030244295, (43, 27290): 356.05854971382274, (43, 27295): 358.49172040904295, (43, 27300): 355.0467548215703, (43, 27344): 353.40610905612436, (43, 27366): 350.86796171911067, (43, 27383): 351.1187254867164, (43, 27398): 352.36905732347424, (43, 27406): 354.4067226737045, (43, 27407): 354.9538736725486, (43, 27426): 364.21860474780016, (43, 27432): 367.11703879517, (43, 27460): 366.29904996485647, (43, 27523): 333.50225523309405, (43, 27545): 332.1202005985185, (43, 27602): 301.8046776877131, (43, 27606): 303.0921977016679, (43, 27646): 304.8929025955943, (43, 27667): 298.3077168185566, (43, 27672): 298.87118681001897, (43, 27674): 299.4131429510245, (43, 27688): 302.05406632735134, (43, 27692): 296.72439708592566, (43, 27693): 297.50017165917876, (43, 27705): 296.5266179922438, (43, 27712): 295.2764439412644, (43, 27786): 342.03429055766367, (43, 27790): 357.9280647148355, (43, 27791): 360.1121750119558, (43, 27795): 341.7092533472394, (43, 27801): 352.2689472921582, (43, 27813): 339.92163536414927, (43, 27816): 343.3287955593162, (43, 27823): 352.7945863688865, (43, 27830): 347.28490516029973, (43, 27884): 306.7425708733811, (43, 27885): 306.18712472518615, (43, 27896): 306.89900243883807, (43, 27919): 307.8691118757733, (43, 27922): 306.4276066635984, (43, 27930): 307.7544653436281, (43, 27934): 306.9088295156222, (43, 27935): 305.95512504203367, (43, 27948): 253.4479724608029, (43, 27951): 268.30205624667053, (43, 28061): 209.64720759636552, (43, 28290): 125.5566340277299, (43, 28292): 120.35351478494093, (43, 28293): 124.22874701773365, (43, 28295): 122.3354709941518, (43, 28296): 124.29486219341211, (43, 28297): 128.05324183814187, (43, 28302): 126.27439618115477, (43, 28310): 181.40856215474278, (43, 28313): 187.42926114760817, (43, 28372): 175.19981371513038, (43, 28398): 176.07785935926609, (43, 28399): 177.00175814403266, (43, 28400): 177.09847203163966, (43, 28401): 175.3403308188701, (43, 28445): 191.2740859043236, (43, 28475): 166.75164100402236, (43, 28885): 696.1070539336948, (43, 28886): 694.8061173138506, (43, 28915): 694.9410237168687, (43, 28916): 694.2720090166699, (43, 28917): 693.4994057279379, (43, 28921): 698.3289086764952, (43, 28931): 697.8161699206446, (43, 28945): 689.6118971621958, (43, 28982): 691.8622714698344, (43, 29219): 693.6151568497744, (43, 29228): 688.9262401928207, (43, 29246): 717.1031279249208, (43, 29248): 715.8160108807075, (43, 29282): 709.7768712764068, (43, 29290): 721.0468404152176, (43, 29291): 719.5589916045284, (43, 29292): 720.8295292004693, (43, 29293): 718.4235731884849, (43, 29294): 719.9741518013058, (43, 29298): 718.37944136599, (43, 29299): 717.9434458336573, (43, 29304): 716.2031876864418, (43, 29317): 710.72984139161, (43, 29323): 710.3306902736606, (43, 29330): 712.9278327518355, (43, 29331): 714.4092681502593, (43, 29344): 692.4122856909615, (43, 29445): 634.8418748763397, (43, 29724): 387.979247141314, (43, 29738): 388.3961386810435, (43, 29745): 388.4979727077434, (43, 29748): 395.394320121159, (43, 29750): 398.8729369764349, (43, 29759): 394.0121977528426, (43, 29772): 395.6506943655277, (43, 29781): 395.4822294520624, (43, 29784): 392.3463213624938, (43, 29790): 397.011621329879, (43, 29811): 399.0275084662336, (43, 29817): 419.3665949095265, (43, 29818): 419.3123042901578, (43, 29929): 384.19907598064844, (43, 30039): 371.3427575563284, (43, 30066): 357.002003763795, (43, 30116): 357.73722974229315, (43, 30238): 361.94326753548773, (43, 30248): 339.94003174355583, (43, 30260): 338.1940088470973, (43, 30545): 682.0591592682175, (43, 30733): 631.8246982306003, (43, 30756): 614.426710869518, (43, 30921): 640.848183911888, (43, 31079): 525.8219054784839, (43, 31149): 516.5995819710942, (43, 31154): 517.0913644750219, (43, 31160): 516.141927085363, (43, 31163): 516.2470165436794, (43, 31189): 493.23298938827156, (43, 31215): 494.9161585703743, (43, 31259): 493.75099826266637, (43, 31262): 491.1766673408743, (43, 31430): 529.1685750117076, (43, 31568): 469.5418912908711, (43, 31751): 514.5103977193698, (44, 109): 212.42209097311323, (44, 872): 644.8182650390993, (44, 873): 647.2575321362216, (44, 877): 646.3271571342505, (44, 879): 646.6875484807823, (44, 884): 644.2026063155641, (44, 889): 645.7387755929913, (44, 891): 643.3994357975699, (44, 892): 648.5817346497095, (44, 894): 648.2799780050565, (44, 896): 645.9551725781862, (44, 903): 646.4013977226537, (44, 909): 642.2985477975716, (44, 910): 643.289914159914, (44, 912): 641.6731370916228, (44, 913): 639.8862693411162, (44, 916): 639.1516006925117, (44, 926): 644.1093514824645, (44, 927): 643.2936162984771, (44, 948): 642.5176081040215, (44, 961): 643.9876392113463, (44, 962): 644.2747076407296, (44, 963): 644.5940936473839, (44, 967): 647.4389838229012, (44, 974): 646.094749366206, (44, 998): 648.391909376216, (44, 1014): 701.8858069795522, (44, 1086): 639.2209570702527, (44, 1087): 638.954448687075, (44, 1089): 636.6793823382661, (44, 1090): 637.7056709123062, (44, 1092): 641.2263461970357, (44, 1097): 638.5328819166081, (44, 1107): 643.004641440046, (44, 1387): 273.68582419177255, (44, 1554): 235.45659919142358, (44, 1827): 755.7854314754329, (44, 1828): 756.0572542073874, (44, 1829): 756.4233574696883, (44, 1830): 755.9774650492369, (44, 1831): 756.2070532036779, (44, 1832): 755.9498985866783, (44, 1833): 755.9895444485679, (44, 1836): 755.7194197681666, (44, 1841): 757.269395269888, (44, 1843): 756.6137563431347, (44, 1844): 756.8955854619004, (44, 1845): 756.106102730056, (44, 1847): 753.6089422063362, (44, 1848): 754.4754173190938, (44, 1849): 758.5262666664115, (44, 1850): 758.9609352440458, (44, 1851): 755.1116052426269, (44, 1852): 755.1518120749886, (44, 1854): 755.585235458175, (44, 1856): 753.4549120298459, (44, 1857): 754.4035271397486, (44, 1858): 758.1476541161711, (44, 1861): 756.3485677842671, (44, 1866): 753.3794450958278, (44, 1867): 757.3342771596717, (44, 1868): 756.8269297909699, (44, 1870): 756.7932679343398, (44, 1871): 757.2349307250763, (44, 1875): 755.5569688505047, (44, 1880): 754.0188626864431, (44, 1882): 754.2420285727212, (44, 1883): 759.0211011898988, (44, 1889): 754.5111987378452, (44, 1893): 756.5084986065359, (44, 1894): 755.900081746874, (44, 1899): 753.9847072978531, (44, 1900): 754.445707570824, (44, 1902): 757.5754490168866, (44, 1905): 758.3535419706686, (44, 1907): 755.0900146652689, (44, 1910): 755.410938688997, (44, 1917): 760.097793698863, (44, 1920): 755.1697636731146, (44, 1935): 758.5060461646725, (44, 1937): 759.1744391433477, (44, 1946): 752.669391228127, (44, 1949): 753.4377673281934, (44, 1950): 750.7230106328267, (44, 1951): 752.0208507652527, (44, 1952): 752.9244229138172, (44, 1953): 753.3943033899938, (44, 1954): 752.7512987545375, (44, 1958): 753.1988503151916, (44, 1960): 754.4712467405151, (44, 1968): 754.9734964198922, (44, 1969): 758.7043455737277, (44, 1974): 757.7249637751959, (44, 1975): 757.7010431251524, (44, 1979): 755.8986375564026, (44, 1980): 755.7149871242834, (44, 1981): 756.2747317875721, (44, 1985): 756.7261926234855, (44, 1994): 749.5957471454616, (44, 2011): 754.1957769668655, (44, 2019): 760.5240918683411, (44, 2020): 759.686927708672, (44, 2029): 756.469486566959, (44, 2030): 759.1072955904335, (44, 2032): 755.9233573013369, (44, 2033): 757.6520934746948, (44, 2034): 757.602850114487, (44, 2036): 754.3107357604968, (44, 2037): 755.1565274546148, (44, 2038): 755.525413204656, (44, 2042): 765.2400851155697, (44, 2050): 757.2431234950838, (44, 2051): 757.0818033636007, (44, 2053): 757.3489561080639, (44, 2054): 758.2077945897066, (44, 2066): 756.4563307670957, (44, 2067): 756.4727294421494, (44, 2071): 747.9844361106954, (44, 2072): 749.6114310249153, (44, 2073): 745.2364885201606, (44, 2074): 745.0057062356127, (44, 2080): 742.2508013119402, (44, 2082): 750.4843831422966, (44, 2083): 751.3268764147159, (44, 2089): 749.5696037182175, (44, 2090): 750.3586842388196, (44, 2092): 749.3067797301495, (44, 2098): 743.317058040642, (44, 2099): 744.2463269761162, (44, 2101): 743.131892019487, (44, 2102): 747.5556416943226, (44, 2103): 746.1585256553229, (44, 2104): 745.3872693540043, (44, 2106): 751.8834923338372, (44, 2112): 743.7059767035747, (44, 2113): 748.1760656328217, (44, 2114): 749.216337409764, (44, 2117): 752.5338217023401, (44, 2123): 746.6003735041792, (44, 2124): 747.5123366649353, (44, 2134): 744.8878929983249, (44, 2138): 747.5816451072, (44, 2141): 745.2119292128338, (44, 2148): 746.4424811087575, (44, 2150): 742.9875164448074, (44, 2151): 743.939985014591, (44, 2152): 742.4764214249021, (44, 2153): 746.7605528552523, (44, 2154): 742.9885726138679, (44, 2155): 742.5354891015826, (44, 2156): 741.8453723166863, (44, 2157): 742.7370458340481, (44, 2160): 748.8082254535792, (44, 2161): 742.3090966130516, (44, 2162): 746.8786450352511, (44, 2163): 745.6011243213968, (44, 2164): 745.5087285352614, (44, 2168): 743.3042158838335, (44, 2172): 744.1080539484318, (44, 2174): 743.817046752141, (44, 2178): 744.8420931956671, (44, 2179): 744.2481483687388, (44, 2183): 747.5079222610614, (44, 2185): 747.5592837056424, (44, 2186): 746.8345535861268, (44, 2190): 748.9979451394928, (44, 2192): 747.6909035137587, (44, 2193): 747.7669805605748, (44, 2194): 746.431822053782, (44, 2195): 746.2257545285454, (44, 2197): 747.9707259391608, (44, 2205): 746.0839118315617, (44, 2207): 743.6325147394459, (44, 2208): 745.0009874541385, (44, 2212): 748.1849875272056, (44, 2214): 720.9917383489565, (44, 2225): 724.1516834747591, (44, 2231): 718.1430311140083, (44, 2278): 737.3376409760712, (44, 2284): 740.0566643512428, (44, 2285): 739.660498753932, (44, 2291): 734.1220358718899, (44, 2292): 734.8159288458236, (44, 2307): 738.2679017698862, (44, 2313): 733.4448622120893, (44, 2317): 732.8251991607264, (44, 2319): 735.7517488621096, (44, 2321): 736.997120813463, (44, 2323): 736.8589716523643, (44, 2326): 741.7166614455776, (44, 2327): 740.5270409426167, (44, 2329): 739.7121665113535, (44, 2330): 738.777224504523, (44, 2332): 740.7237725972174, (44, 2344): 737.7306450801117, (44, 2346): 737.6554856042726, (44, 2361): 737.3541381244662, (44, 2368): 751.1393544283917, (44, 2374): 752.4336391786326, (44, 2375): 752.8814344923974, (44, 2377): 748.3249007893083, (44, 2378): 753.6976976856969, (44, 2379): 753.7928756716257, (44, 2380): 754.2584544748426, (44, 2383): 749.5561733631508, (44, 2385): 750.2687162225233, (44, 2395): 750.3646043869502, (44, 2397): 753.2403883138426, (44, 2398): 746.8710782029851, (44, 2399): 748.5242992095556, (44, 2400): 748.156030844219, (44, 2402): 750.7097966203148, (44, 2403): 751.7296102652618, (44, 2404): 752.0008172379945, (44, 2405): 749.5354792048594, (44, 2407): 751.5561169502333, (44, 2408): 752.7441522566077, (44, 2409): 750.286539258427, (44, 2411): 751.6870828048535, (44, 2412): 751.4327074855057, (44, 2413): 752.2645314311263, (44, 2414): 750.8994745564772, (44, 2422): 751.3641152271299, (44, 2424): 751.7283332948467, (44, 2426): 751.956475843832, (44, 2433): 750.041311226304, (44, 2436): 749.5121159728732, (44, 2437): 743.5624752681147, (44, 2440): 744.880093103964, (44, 2445): 771.015383854657, (44, 2447): 767.8001691559878, (44, 2454): 770.8501518488713, (44, 2455): 771.0405158913054, (44, 2460): 761.5417983834659, (44, 2461): 762.7096245357269, (44, 2471): 781.4886110493818, (44, 2492): 760.4527763697956, (44, 2511): 751.1498498980662, (44, 2523): 755.9041461873956, (44, 2525): 754.4130487381764, (44, 2535): 757.4656243781911, (44, 2537): 755.3518618634912, (44, 2538): 756.8397523383518, (44, 2539): 756.0807601027153, (44, 2540): 758.4208498063028, (44, 2542): 759.9003045118353, (44, 2559): 790.0557800228524, (44, 2575): 787.1815361913364, (44, 2599): 742.3883610150361, (44, 2600): 752.4118813044923, (44, 2607): 746.7299751788345, (44, 2627): 756.4362051330766, (44, 2647): 761.8751297215252, (44, 2674): 759.2009106302647, (44, 2681): 758.3431680451982, (44, 2683): 761.0910071555093, (44, 2686): 758.0221978444396, (44, 2689): 794.0849824182022, (44, 2690): 794.2400017747863, (44, 2713): 800.6262020548603, (44, 2714): 801.1542963792439, (44, 2715): 802.0479683423, (44, 2739): 801.2788571234157, (44, 2740): 795.8638021439206, (44, 2741): 796.323990981883, (44, 2749): 799.9608007779572, (44, 2750): 800.2684321516772, (44, 2752): 800.9185038562462, (44, 2755): 801.6073218929092, (44, 2758): 801.3773508559128, (44, 2759): 801.3931069130036, (44, 2769): 800.3872131264749, (44, 2771): 797.2487442271732, (44, 2779): 797.3233801731024, (44, 2784): 787.1766421787187, (44, 2800): 788.7761887248721, (44, 2802): 794.0256700296551, (44, 2803): 793.7108550329843, (44, 2804): 793.123743587609, (44, 2805): 794.702673468655, (44, 2807): 794.6722254343365, (44, 2809): 794.2831255870248, (44, 2812): 788.6128846933001, (44, 2814): 793.8141283582719, (44, 2817): 793.7855278203024, (44, 2819): 794.8507512097258, (44, 2823): 788.951659368203, (44, 2832): 795.7771236540958, (44, 2836): 791.7564162101414, (44, 2839): 794.6850308809377, (44, 2841): 794.0985386668411, (44, 2843): 793.840135618832, (44, 2846): 792.4477501408796, (44, 2849): 796.3617286029527, (44, 2852): 795.4648416320498, (44, 2853): 796.7729911683236, (44, 2876): 797.0614530794558, (44, 2877): 800.2695296900382, (44, 2885): 801.0040056041536, (44, 2918): 795.4666686593682, (44, 2921): 796.8247781503575, (44, 2925): 790.5265895387176, (44, 2926): 788.4655360671362, (44, 2930): 792.9887188052736, (44, 2931): 791.0604679350657, (44, 2938): 795.4417073282561, (44, 2940): 799.6705072127868, (44, 2947): 794.9840603340486, (44, 2949): 793.0435226773903, (44, 2950): 793.6258204638189, (44, 2952): 792.9397589346557, (44, 2958): 792.8233087217956, (44, 2959): 793.5313194923199, (44, 2960): 795.0407872346625, (44, 2961): 794.2894688493471, (44, 2963): 792.2191637304774, (44, 2968): 792.6303900064198, (44, 2976): 792.0620618414431, (44, 2981): 778.7333758740363, (44, 2982): 778.309057419447, (44, 2984): 777.6197145362702, (44, 3003): 776.3747346556735, (44, 3046): 768.0408252402542, (44, 3050): 774.7610498937455, (44, 3051): 775.3155605927437, (44, 3053): 773.7990262113095, (44, 3069): 782.0852109230663, (44, 3071): 773.5459045879568, (44, 3080): 800.9396538417067, (44, 3199): 773.8712481619542, (44, 3200): 772.2585679740363, (44, 3205): 782.0325985116392, (44, 3209): 773.0797228579224, (44, 3215): 772.3812614153786, (44, 3217): 770.4273582872307, (44, 3249): 772.5850852864165, (44, 3263): 787.3493199174306, (44, 3289): 777.3147758801847, (44, 3301): 777.7205767263806, (44, 3302): 777.0398658657289, (44, 3307): 776.1693292657368, (44, 3310): 778.5615784024258, (44, 3391): 779.1383920160008, (44, 3509): 464.5028694780871, (44, 3510): 463.11337639659166, (44, 3511): 464.08002760250537, (44, 3512): 463.25679616822333, (44, 3514): 463.5817553701748, (44, 3519): 467.5644298647538, (44, 3536): 467.02671353340367, (44, 3545): 469.24884791795535, (44, 3548): 467.17247880946223, (44, 3572): 467.7658136641235, (44, 3581): 465.94660564427386, (44, 3583): 465.1685332637114, (44, 3601): 470.113480338622, (44, 3656): 467.70871317672515, (44, 3669): 464.6818745363138, (44, 3670): 465.9160931676786, (44, 3695): 458.9193904670539, (44, 3696): 459.9098250866239, (44, 3782): 468.4217299383967, (44, 3792): 466.7784567284725, (44, 3989): 132.6677649415836, (44, 4008): 140.39325511039877, (44, 4031): 140.71415051709965, (44, 4045): 137.1849431311448, (44, 4144): 136.96381117003332, (44, 4145): 128.72967516011167, (44, 4164): 133.85035475183602, (44, 4168): 131.2063987120454, (44, 4173): 130.60920865615478, (44, 4181): 125.94623339292706, (44, 4228): 122.0516491701326, (44, 4248): 119.50332175528632, (44, 4254): 81.55990804907145, (44, 4260): 81.08660243689901, (44, 4262): 83.8400344070479, (44, 4273): 82.95871530640828, (44, 4319): 67.63138015865015, (44, 4326): 66.7929567467139, (44, 4328): 66.64762809309728, (44, 4334): 68.6837562113848, (44, 4335): 68.53548285915902, (44, 4372): 254.29588977739826, (44, 4413): 274.37581122396426, (44, 4434): 252.17794847823, (44, 4447): 249.39512423675905, (44, 4452): 253.10870010025036, (44, 4463): 259.148137580663, (44, 4465): 257.9324841897372, (44, 4619): 290.376461583815, (44, 4645): 290.16142111021526, (44, 4657): 291.6226525426993, (44, 4666): 292.43971927307257, (44, 4676): 293.7884886648837, (44, 4678): 293.25490476146166, (44, 4689): 294.43288345570045, (44, 4704): 301.85414359507945, (44, 4726): 358.03665853283195, (44, 4727): 357.1483544208948, (44, 4730): 355.3167905911227, (44, 4731): 356.56529523807643, (44, 4734): 353.40414459383607, (44, 4735): 353.1837435206102, (44, 4736): 354.14882007949564, (44, 4737): 353.3907897891048, (44, 4738): 354.0269893072173, (44, 4756): 355.24634924763166, (44, 4760): 347.7455674288868, (44, 4761): 347.0229877713445, (44, 4762): 347.27722835560155, (44, 4765): 348.54860761361977, (44, 4773): 359.18423723915686, (44, 4774): 359.3793984212732, (44, 4790): 358.44579132494084, (44, 4795): 357.4223442786549, (44, 4799): 360.2860552149685, (44, 4801): 363.4935799994619, (44, 4804): 356.48801188864724, (44, 4805): 355.6610919639748, (44, 4806): 360.49901923523896, (44, 4815): 360.51942376738964, (44, 4816): 362.28946392324525, (44, 4817): 363.86365679067364, (44, 4826): 362.1932726798562, (44, 4830): 361.42118298596705, (44, 4839): 350.3862928248432, (44, 4840): 351.6693764759045, (44, 4841): 350.2007272516808, (44, 4846): 349.39272661750266, (44, 4848): 350.18281520775554, (44, 4850): 351.1558852396143, (44, 4871): 336.34545388487123, (44, 4883): 345.3026380788391, (44, 4900): 339.2933342160819, (44, 4901): 338.9888409497958, (44, 4917): 310.6509669600773, (44, 4931): 306.0258460826632, (44, 4944): 310.4043892933859, (44, 4956): 307.6463742979868, (44, 4958): 309.05138903042206, (44, 4959): 309.23665179276003, (44, 4961): 307.9513581577313, (44, 4966): 307.4173242160128, (44, 5207): 302.55288812555244, (44, 5272): 176.66792267252623, (44, 5283): 178.18413952766323, (44, 5287): 184.8705402317362, (44, 5289): 185.7163140959519, (44, 5293): 172.78558629439678, (44, 5295): 176.5076068630027, (44, 5296): 179.06128231610055, (44, 5298): 180.4538098951987, (44, 5303): 183.78736551006688, (44, 5305): 180.94374450301692, (44, 5306): 183.6177704521174, (44, 5307): 180.50114428819506, (44, 5308): 182.37968861342637, (44, 5313): 179.06275144103313, (44, 5314): 178.90826044311476, (44, 5317): 184.07370969619785, (44, 5319): 183.09156024435472, (44, 5324): 180.35807876643167, (44, 5326): 178.44985466546916, (44, 5348): 185.54927181352227, (44, 5351): 190.09792435498466, (44, 5399): 190.2402126639003, (44, 5413): 197.42256909336965, (44, 5422): 188.43201095878032, (44, 5445): 186.51028987692675, (44, 5448): 185.31604035952486, (44, 5456): 187.7672065417509, (44, 5467): 189.59398191945152, (44, 5624): 169.13605271064662, (44, 5671): 177.594354696152, (44, 5672): 174.94364043285148, (44, 5797): 209.02938796048568, (44, 5871): 233.09377051197353, (44, 5976): 218.2410743044364, (44, 6118): 630.9143264540148, (44, 6248): 660.5926957677749, (44, 6345): 152.53974968372555, (44, 6352): 159.4207432161687, (44, 6354): 150.74814679357274, (44, 6359): 149.59273463617856, (44, 6376): 158.89827230235954, (44, 6378): 151.58423903672735, (44, 6381): 150.3013204214699, (44, 6383): 153.91489572677975, (44, 6396): 152.03087353255648, (44, 6399): 152.71071414960358, (44, 6408): 158.95645238509294, (44, 6409): 155.22850289943258, (44, 6419): 165.54225300845863, (44, 6422): 157.64655818327302, (44, 6423): 158.17126848932543, (44, 6424): 150.88063899734482, (44, 6439): 152.04743608350742, (44, 6464): 153.79942875647566, (44, 6465): 154.62379007075205, (44, 6469): 154.11083637329534, (44, 6470): 154.6136988885187, (44, 6472): 147.34461112631584, (44, 6480): 147.958258219671, (44, 6486): 143.34699474314579, (44, 6497): 144.82463258153817, (44, 6503): 152.6664567396253, (44, 6508): 152.52419726812064, (44, 6509): 151.06250745560087, (44, 6521): 146.81546476808217, (44, 6544): 146.9329157676327, (44, 6552): 155.7137745467629, (44, 6553): 156.72303103923724, (44, 6554): 157.7550196945762, (44, 6578): 154.08448647983258, (44, 6582): 154.46934068738756, (44, 6601): 153.53467688665728, (44, 6609): 145.7905540813181, (44, 6610): 145.39316813544679, (44, 6611): 145.47201898399706, (44, 6614): 146.190261842605, (44, 6615): 145.892417828403, (44, 6616): 144.44909910551678, (44, 6617): 145.04429713578347, (44, 6618): 143.18682834367365, (44, 6619): 146.87535092110062, (44, 6620): 144.2677611017499, (44, 6621): 145.11215107442086, (44, 6622): 145.01478345674784, (44, 6623): 146.07733098355675, (44, 6624): 146.6722194820556, (44, 6625): 146.93107395639592, (44, 6626): 147.00946282054406, (44, 6627): 146.58175597774652, (44, 6628): 144.29925157922867, (44, 6629): 146.22672473141367, (44, 6630): 147.98568445667178, (44, 6632): 146.40569839909463, (44, 6634): 148.81050741958984, (44, 6635): 145.51052343234835, (44, 6636): 144.34333966393228, (44, 6637): 147.41270595932653, (44, 6638): 147.69665690962404, (44, 6639): 146.37276238561734, (44, 6640): 147.64428320455184, (44, 6641): 145.01977134221846, (44, 6642): 147.55520823423132, (44, 6643): 147.25237501779623, (44, 6645): 146.6662699523274, (44, 6646): 143.62243854074976, (44, 6647): 147.35734508539045, (44, 6653): 145.9910607269941, (44, 6655): 146.42806082686454, (44, 6658): 148.80253705320297, (44, 6662): 147.48143298038792, (44, 6819): 195.95854275351752, (44, 6996): 179.31446203250408, (44, 7059): 167.84059629507456, (44, 7187): 195.3686913583738, (44, 7304): 213.54834880779762, (44, 7528): 182.55022241816357, (44, 7720): 113.3526047648631, (44, 7793): 116.31796712223732, (44, 7807): 114.8480545490167, (44, 7808): 117.07665520969832, (44, 7831): 138.5037612722746, (44, 7850): 128.00769455228684, (44, 7852): 130.78105085169724, (44, 8012): 115.10500513617663, (44, 8125): 122.8861919008434, (44, 8208): 93.53178981017503, (44, 8392): 130.33198986839903, (44, 8651): 251.77093266767397, (44, 9088): 202.81886462773238, (44, 9443): 282.92215041863, (44, 9444): 281.5122763868678, (44, 9828): 337.9297885263814, (44, 9868): 334.2230267881592, (44, 10180): 123.92871029856741, (44, 10256): 105.72351682416686, (44, 10276): 109.52347914856065, (44, 10378): 95.42289719347399, (44, 10676): 149.97109612523565, (44, 10714): 168.40576602596664, (44, 10730): 152.2953925955967, (44, 10862): 327.45677947312697, (44, 10881): 327.2850348449786, (44, 10883): 328.01834156529037, (44, 10885): 327.3209699040184, (44, 10891): 329.177691129859, (44, 10909): 327.48540970181284, (44, 10911): 325.70917658565975, (44, 10913): 326.3139422607994, (44, 10915): 325.41209729524064, (44, 10919): 324.6288810705626, (44, 11037): 348.06477126411204, (44, 11039): 341.85515699550626, (44, 11516): 226.9246462376148, (44, 11856): 69.33197803189819, (44, 11857): 70.02707983849119, (44, 11861): 69.7308014055403, (44, 11881): 66.60202206900351, (44, 11902): 62.03860381626524, (44, 11911): 59.689523132709844, (44, 11914): 60.977148777468756, (44, 11922): 64.90559041453743, (44, 11924): 65.62036090324457, (44, 11926): 64.20095707542065, (44, 11950): 65.37990999596792, (44, 11963): 70.06326771433861, (44, 11983): 64.91692324727923, (44, 11985): 72.53002114240165, (44, 12009): 69.90480349566116, (44, 12010): 66.94934646693497, (44, 12018): 67.2749412602313, (44, 12020): 68.42427719287971, (44, 12021): 68.79624728475247, (44, 12024): 72.00097172211728, (44, 12025): 71.25206142157568, (44, 12027): 70.41066984375148, (44, 12031): 66.40074244948714, (44, 12032): 67.78259690917795, (44, 12035): 69.33351095769143, (44, 12041): 74.05501394695773, (44, 12045): 29.993688982354765, (44, 12145): 46.50287069640593, (44, 12275): 137.94455871115616, (44, 12294): 131.94895413353078, (44, 12358): 158.1932969444882, (44, 12463): 169.63828543191104, (44, 12465): 169.46850477971844, (44, 12482): 172.03298574698107, (44, 12503): 171.83822046263953, (44, 12506): 172.9417499422992, (44, 12549): 168.74625915053488, (44, 12559): 168.2451261746504, (44, 12569): 169.79194927320003, (44, 12572): 170.58861889077428, (44, 12574): 168.7240421718293, (44, 12576): 169.51240263833668, (44, 12591): 168.36542086179625, (44, 12608): 174.6212223258799, (44, 12696): 162.99064547937454, (44, 12710): 168.4359279406858, (44, 12728): 166.38109058537503, (44, 12766): 76.59989640478919, (44, 12771): 73.752391265183, (44, 12790): 74.923990621868, (44, 12795): 78.6106933583712, (44, 12797): 83.20011340381517, (44, 12798): 81.64938002003642, (44, 12811): 74.78095906236298, (44, 12830): 78.35717038083094, (44, 12848): 74.47715937639124, (44, 12850): 72.31911999409802, (44, 12852): 77.86433692816024, (44, 12854): 78.93191866025767, (44, 12859): 72.71153288367303, (44, 12861): 79.85791627234269, (44, 12865): 74.78814894140038, (44, 12866): 74.45992238770242, (44, 12867): 73.23831084339501, (44, 12874): 73.93461318966085, (44, 12875): 72.81762837672227, (44, 12881): 76.90114293596054, (44, 12883): 75.5543314692153, (44, 12885): 72.37273695532602, (44, 12888): 75.57976104847883, (44, 12889): 75.32729904800497, (44, 12892): 74.0538317208062, (44, 12893): 76.10846749842192, (44, 12896): 74.91842954192418, (44, 12906): 76.54075021057918, (44, 13018): 101.3591975034686, (44, 13071): 105.06414234267133, (44, 13131): 99.43218403820873, (44, 13146): 89.48726880379054, (44, 13159): 116.3076134988284, (44, 13193): 100.03986080721657, (44, 13198): 110.08707456013362, (44, 13292): 92.10033422684157, (44, 13296): 83.03823984481339, (44, 13406): 125.74602376504244, (44, 13407): 126.76846845855191, (44, 13417): 132.39852824682583, (44, 13418): 131.6724526415789, (44, 13438): 121.74816310717398, (44, 13442): 118.93877067085953, (44, 13443): 120.34156356842698, (44, 13764): 260.80980553810696, (44, 13766): 259.0787500154136, (44, 13771): 262.30062619168035, (44, 13783): 259.76917842068593, (44, 13784): 256.53371288298547, (44, 13792): 267.96621890889736, (44, 13824): 261.25863594685757, (44, 14017): 242.79726386428348, (44, 14870): 291.05384249166264, (44, 14997): 204.37356199744565, (44, 15000): 204.55004096188298, (44, 15003): 203.7545567565162, (44, 15006): 199.62045257757225, (44, 15007): 198.47208772194713, (44, 15056): 199.66170145520925, (44, 15063): 200.923465057518, (44, 15069): 201.7434739684945, (44, 15076): 198.52012217456948, (44, 15086): 201.81897343034646, (44, 15087): 203.5380510283965, (44, 15111): 206.78242854569845, (44, 15116): 204.94677596033316, (44, 15722): 236.35640120178056, (44, 15998): 266.60450163604344, (44, 16073): 523.7153616322073, (44, 16939): 677.5857940103692, (44, 16940): 675.7942555059865, (44, 16951): 677.7448078362347, (44, 16963): 677.9389858165564, (44, 16965): 680.1586176058892, (44, 16969): 679.5735563581122, (44, 16970): 678.7597820161162, (44, 16971): 676.7630759006018, (44, 16973): 676.5974042808688, (44, 16974): 681.0204410452747, (44, 16976): 678.9346611810638, (44, 16978): 677.4869892685031, (44, 16980): 679.6996364489592, (44, 16982): 680.9718662776772, (44, 17045): 739.5339302215245, (44, 17048): 742.0915315101261, (44, 17304): 108.36325912174148, (44, 17305): 107.24698752454259, (44, 17330): 108.39521664356988, (44, 17334): 105.87536264286261, (44, 17343): 110.28356790834273, (44, 17345): 105.92810951316596, (44, 17347): 108.3604249155041, (44, 17351): 102.52027618542544, (44, 17372): 105.64196463610081, (44, 17373): 110.10964161737414, (44, 17377): 110.43963584576646, (44, 17382): 107.56001581824555, (44, 17383): 108.03932412367642, (44, 17389): 106.35411248177509, (44, 17400): 109.25709904510138, (44, 17401): 109.17784109206168, (44, 17402): 109.44181772008345, (44, 17403): 109.74173398499224, (44, 17440): 106.37471519805058, (44, 17455): 109.92860412860186, (44, 17491): 110.42189148704102, (44, 17507): 104.24280045589536, (44, 17509): 105.86755130079894, (44, 17590): 101.61640525552046, (44, 17615): 93.95464376402519, (44, 17642): 95.23828979404941, (44, 17643): 94.9171812903367, (44, 17668): 94.03534266988696, (44, 17721): 92.08517896905391, (44, 17754): 106.90975223175269, (44, 17769): 105.02350999279152, (44, 17776): 98.36133479716634, (44, 17804): 107.63566895312451, (44, 17809): 109.2192704128277, (44, 17824): 108.39314421743236, (44, 17837): 103.1616883711828, (44, 17838): 103.31794129678077, (44, 17862): 102.13326079731486, (44, 17866): 105.52949767625553, (44, 17872): 100.98424532298415, (44, 17873): 98.38788719757767, (44, 17881): 102.37303639370768, (44, 17947): 531.239308023033, (44, 17951): 527.801595154008, (44, 17953): 527.1473054973945, (44, 17954): 527.3895964512445, (44, 17959): 530.5287174364729, (44, 17963): 529.3138110469516, (44, 18000): 511.838672466972, (44, 18001): 512.5286828730913, (44, 18111): 561.8529803668949, (44, 18148): 474.1169788383812, (44, 18166): 508.2122132624969, (44, 18189): 539.7195456606994, (44, 18239): 110.86258170102562, (44, 18240): 110.85089694603444, (44, 18245): 111.01607927546327, (44, 18247): 110.67395306822449, (44, 18251): 111.02001129648991, (44, 18256): 111.40669363884213, (44, 18258): 111.01067886225931, (44, 18259): 111.08940584103622, (44, 18260): 111.25497929802117, (44, 18262): 111.56129400258358, (44, 18263): 111.5184707735766, (44, 18264): 111.68187677015185, (44, 18266): 111.69331102178167, (44, 18267): 111.85344441451825, (44, 18268): 111.93829462982293, (44, 18269): 112.26121090303641, (44, 18275): 112.10872773152451, (44, 18285): 111.62166080932595, (44, 18308): 108.39340551637734, (44, 18313): 107.3222346626891, (44, 18314): 107.79990269907415, (44, 18315): 112.20066010979716, (44, 18316): 112.19463203236623, (44, 18317): 112.34659484069736, (44, 18320): 112.45899079286605, (44, 18321): 112.551627553641, (44, 18322): 112.78694571560966, (44, 18324): 112.94772644076188, (44, 18325): 113.64863183928388, (44, 18326): 113.38651599144903, (44, 18327): 112.5062104394528, (44, 18329): 113.94091224946824, (44, 18330): 113.6594064272051, (44, 18331): 113.17741037904055, (44, 18332): 112.69387192655395, (44, 18333): 113.56449630799018, (44, 18336): 113.13863104482635, (44, 18337): 113.36428724521951, (44, 18403): 113.14693934088373, (44, 18432): 105.15473859719599, (44, 18451): 110.42229075494396, (44, 18466): 116.1311621269179, (44, 18481): 112.33878058171474, (44, 18483): 112.3492156694434, (44, 18484): 111.95641377083486, (44, 18485): 110.77378907219068, (44, 18486): 111.7838602988705, (44, 18487): 110.89200549323019, (44, 18489): 111.6940350324349, (44, 18490): 112.56799346343786, (44, 18491): 112.98720279304185, (44, 18492): 109.99954968468847, (44, 18493): 111.6318142396602, (44, 18494): 111.52922540129599, (44, 18495): 112.25500900699784, (44, 18496): 111.81945103586243, (44, 18497): 110.68666956948643, (44, 18498): 110.90025014335286, (44, 18499): 111.55520702003726, (44, 18501): 111.07410981713768, (44, 18502): 110.65606663296087, (44, 18503): 110.33860613743626, (44, 18504): 112.00007481559955, (44, 18506): 111.13196440728716, (44, 18507): 110.73576390866435, (44, 18508): 111.45913224656958, (44, 18509): 111.46374102865272, (44, 18510): 110.34589931662143, (44, 18511): 111.75502571289151, (44, 18512): 111.26472471516998, (44, 18515): 112.03154989132031, (44, 18516): 112.05327801477057, (44, 18517): 111.52661471087454, (44, 18518): 112.39993826776261, (44, 18519): 112.094829392717, (44, 18520): 111.3413684736279, (44, 18522): 113.90120723830454, (44, 18523): 113.9801221524618, (44, 18532): 114.5477126347026, (44, 18535): 113.35681898656719, (44, 18537): 112.69414410456677, (44, 18539): 112.82630747001457, (44, 18540): 112.89713295046978, (44, 18541): 113.21884646431717, (44, 18542): 113.42435217210685, (44, 18543): 112.40011187883177, (44, 18546): 112.86987305815994, (44, 18555): 113.91121303318168, (44, 18556): 114.09593659172079, (44, 18565): 114.4564635836626, (44, 18567): 114.74426906205242, (44, 18568): 114.18275380191261, (44, 18577): 118.26368485270297, (44, 18583): 117.59932923107932, (44, 18605): 118.49161776569564, (44, 18608): 115.07794671558766, (44, 18616): 122.28871261683938, (44, 18618): 125.51673133539664, (44, 18625): 124.48116415450886, (44, 18645): 121.68896592649443, (44, 18646): 122.38490616863757, (44, 18653): 119.59207460640508, (44, 18654): 122.19511921082074, (44, 18655): 120.46974018845401, (44, 18666): 131.11816120850406, (44, 18837): 128.56252198431534, (44, 18974): 111.65748411204186, (44, 18999): 115.16885598790262, (44, 19000): 116.1110231161501, (44, 19174): 86.07638270476531, (44, 19342): 105.71118978741647, (44, 19455): 82.03219689568462, (44, 19555): 58.87257920114349, (44, 19564): 69.59176268032931, (44, 19573): 66.77789709409033, (44, 19586): 64.89383735458036, (44, 19605): 63.60723018815628, (44, 19611): 65.15045461626033, (44, 19614): 61.81315733677106, (44, 19641): 78.67839024626758, (44, 19702): 80.98742314060904, (44, 19713): 79.09108668771248, (44, 19731): 41.63537261602297, (44, 19819): 79.56556792894769, (44, 19893): 105.82413106752838, (44, 19899): 117.92610551496796, (44, 19929): 106.56346871959035, (44, 19951): 123.51959943336192, (44, 19962): 112.31367839465327, (44, 19970): 106.74913303818143, (44, 19971): 108.90954480509114, (44, 19972): 109.07577119975674, (44, 19975): 106.97646998063618, (44, 19978): 118.44656777285022, (44, 19987): 117.45276667128446, (44, 19989): 112.35016824735028, (44, 20039): 117.77199997283859, (44, 20043): 118.17122382700248, (44, 20047): 114.89351194852985, (44, 20052): 110.63391302543535, (44, 20054): 111.94323161810213, (44, 20085): 128.00110988539987, (44, 20104): 129.48264528843842, (44, 20132): 122.32608624388287, (44, 20203): 124.60590708624662, (44, 20280): 129.4424697943822, (44, 20285): 131.72563617620284, (44, 20290): 128.81323725078042, (44, 20297): 127.1901807178696, (44, 20309): 133.67067985113448, (44, 20453): 147.84591402738505, (44, 20485): 118.36240686286432, (44, 20520): 114.6760971875601, (44, 20526): 120.46663862033026, (44, 20698): 335.4401989251721, (44, 20868): 398.11026502225883, (44, 21042): 60.317237290880755, (44, 21057): 47.03143672287476, (44, 21066): 54.267153057417254, (44, 21075): 55.76647794806304, (44, 21093): 60.33700082611642, (44, 21098): 53.04025445201673, (44, 21127): 59.736049546928754, (44, 21130): 57.77940229364508, (44, 21144): 57.16879123644983, (44, 21146): 60.59590978219274, (44, 21147): 57.140626670735124, (44, 21148): 55.13686628318154, (44, 21153): 58.971050622369965, (44, 21293): 39.97579879632496, (44, 21426): 45.49917103373971, (44, 21442): 39.96216987520218, (44, 21451): 39.62571202404913, (44, 21466): 40.92459385689019, (44, 21469): 39.015728218826936, (44, 21471): 41.94283294439113, (44, 21473): 40.108776977228295, (44, 21475): 41.48094052270277, (44, 21482): 38.70221206361284, (44, 21484): 38.623496977465216, (44, 21488): 39.963483548808945, (44, 21494): 40.41160956066574, (44, 21498): 39.22694863660794, (44, 21500): 40.327864731815595, (44, 21514): 33.45196975223656, (44, 21537): 38.776791902649144, (44, 21662): 30.137216182138296, (44, 21691): 38.012891494242446, (44, 21757): 56.08273396917261, (44, 21777): 89.25554873091023, (44, 21778): 91.17770355741419, (44, 21779): 90.76629687708034, (44, 21790): 86.39742380202858, (44, 21802): 87.79513491378741, (44, 21824): 86.54711969319476, (44, 21874): 91.13710835800775, (44, 21879): 93.62473074760017, (44, 21983): 79.15547742017593, (44, 22002): 63.31488651299324, (44, 22132): 69.6815145310497, (44, 22261): 362.6743518451393, (44, 22298): 359.2506547072837, (44, 22339): 385.1566220731204, (44, 22508): 322.3998724782999, (44, 22841): 767.4988265270363, (44, 22842): 767.5852647783114, (44, 22874): 762.8979123983713, (44, 22941): 763.1450927531499, (44, 22956): 766.233809010675, (44, 22960): 766.941954412242, (44, 22968): 770.9460981687474, (44, 22970): 771.6313248914855, (44, 22974): 773.7437394479556, (44, 22980): 777.3819107426079, (44, 23025): 777.8730363178818, (44, 23028): 777.233144848161, (44, 23081): 784.3581199530942, (44, 23104): 779.1109936983127, (44, 23147): 744.7240003451639, (44, 23298): 24.0, (44, 23376): 24.0, (44, 23381): 24.0, (44, 23529): 24.0, (44, 23556): 24.0, (44, 23718): 24.0, (44, 24001): 39.91223723590708, (44, 24094): 49.644989675046865, (44, 24129): 55.368020849697665, (44, 24174): 44.568317992096766, (44, 24235): 57.614729455007364, (44, 24259): 62.20638114555121, (44, 24260): 61.88928247218901, (44, 24261): 60.60056391810878, (44, 24305): 68.48925088652692, (44, 24306): 69.66428218239959, (44, 24307): 67.96172126097149, (44, 24308): 57.327063388755576, (44, 24498): 83.14314639692087, (44, 24499): 83.2459414854647, (44, 24500): 82.1961238444035, (44, 24668): 77.62267186156272, (44, 24711): 90.09848075871166, (44, 24756): 94.11717098424184, (44, 24788): 95.67185240790334, (44, 24809): 89.63152694827201, (44, 24813): 91.43205241400705, (44, 24821): 90.8139835958344, (44, 24825): 91.35405101152197, (44, 24832): 89.15702520647943, (44, 24833): 90.10571456329318, (44, 24835): 91.08063155888101, (44, 24837): 92.53792803336613, (44, 24840): 89.0476394659179, (44, 24841): 90.44084314546116, (44, 24844): 89.1430961051544, (44, 24845): 89.81925568379805, (44, 24846): 90.00633148746712, (44, 24849): 90.54587439807413, (44, 24850): 91.77296600561844, (44, 24863): 78.23580570779733, (44, 24866): 79.89736657752465, (44, 24885): 82.07483825505943, (44, 24886): 82.34534535826545, (44, 24889): 85.7084886436814, (44, 24903): 87.08461949928243, (44, 24909): 80.61176641654873, (44, 24999): 161.1076815996682, (44, 25019): 159.70006778321738, (44, 25028): 159.8379107846809, (44, 25137): 157.26653533675218, (44, 25145): 157.22380089849995, (44, 25208): 182.02189620526568, (44, 25233): 182.33267897063413, (44, 25371): 141.80958812634643, (44, 25377): 137.1102161763474, (44, 25828): 167.89917275254393, (44, 25851): 171.5120604381191, (44, 25874): 162.93482058738874, (44, 25898): 166.4268178253353, (44, 25946): 168.48828665624077, (44, 26047): 166.67058870542738, (44, 26066): 107.99016188930884, (44, 26197): 138.4373334877824, (44, 26212): 229.67544120582284, (44, 26253): 235.9589955117072, (44, 26254): 233.0534136931606, (44, 26257): 232.4975448223509, (44, 26258): 235.1691899441955, (44, 26260): 233.67115829214998, (44, 26266): 232.37071084611676, (44, 26267): 231.15115123282416, (44, 26271): 231.54498067938664, (44, 26304): 207.81490936659205, (44, 26305): 206.79791377250478, (44, 26363): 180.96365131793797, (44, 26441): 378.3230613913941, (44, 26442): 377.6323556367711, (44, 26450): 374.39315911231336, (44, 26459): 374.2507794900244, (44, 26462): 374.75543599194543, (44, 26467): 384.2742803785529, (44, 26471): 381.54797007509916, (44, 26472): 381.24874884369893, (44, 26473): 381.12339482173417, (44, 26476): 379.44761222643615, (44, 26485): 375.8103724847063, (44, 26493): 375.85389254509613, (44, 26524): 376.2370679825986, (44, 26525): 375.83053217182965, (44, 26556): 380.26591921354515, (44, 26560): 380.0483703535592, (44, 26561): 378.01476055637613, (44, 26564): 379.36201674678404, (44, 26569): 377.48081650147464, (44, 26570): 376.6246680468718, (44, 26573): 377.1002542342879, (44, 26581): 376.98729347513756, (44, 26583): 376.29977759347634, (44, 26593): 376.9644764158176, (44, 26837): 384.88082742969533, (44, 26844): 387.07318417187486, (44, 26863): 382.21515952219914, (44, 26893): 388.4886802069965, (44, 26902): 391.461482033104, (44, 26905): 388.52645669261125, (44, 26912): 390.82316005759907, (44, 26921): 385.22517369851613, (44, 26922): 379.1660448443002, (44, 27212): 402.6992752903091, (44, 27218): 400.2157213133356, (44, 27239): 406.8874111105028, (44, 27257): 404.63155849412016, (44, 27274): 407.71154729745376, (44, 27279): 407.17534950294345, (44, 27282): 404.6925766355368, (44, 27283): 405.80071562873565, (44, 27285): 408.79652283390766, (44, 27286): 406.4078516761724, (44, 27290): 402.5595022359457, (44, 27295): 401.1282560925332, (44, 27300): 408.1657049025987, (44, 27344): 401.225492471833, (44, 27366): 403.9748463047826, (44, 27383): 408.87734552068775, (44, 27398): 412.06423032967996, (44, 27406): 409.64296776611263, (44, 27407): 410.4290363866405, (44, 27426): 407.63551887835035, (44, 27432): 396.75308984706277, (44, 27460): 403.63434212151844, (44, 27523): 403.89850280884286, (44, 27545): 448.95867546723804, (44, 27602): 504.9808507136617, (44, 27606): 506.0688640370947, (44, 27646): 446.29371410885534, (44, 27667): 457.5478683068595, (44, 27672): 458.1701276399201, (44, 27674): 456.2318621550559, (44, 27688): 457.96732428139904, (44, 27692): 460.07977812688824, (44, 27693): 458.38853842575054, (44, 27705): 458.26396796849485, (44, 27712): 459.06536801773996, (44, 27786): 508.73711818234926, (44, 27790): 502.7934892007639, (44, 27791): 502.3192286839466, (44, 27795): 505.53764143499876, (44, 27801): 501.0701326250309, (44, 27813): 510.4297685389048, (44, 27816): 508.4520250611033, (44, 27823): 500.9047684580112, (44, 27830): 506.0527221409641, (44, 27884): 427.14743681699554, (44, 27885): 441.51030495121904, (44, 27896): 432.84628791971136, (44, 27919): 432.28492446550837, (44, 27922): 434.02142437815945, (44, 27930): 429.3742481603181, (44, 27934): 429.8938914713014, (44, 27935): 430.26544107793075, (44, 27948): 497.7454377015589, (44, 27951): 501.3158998504627, (44, 28061): 441.6023766219034, (44, 28290): 560.5559480902936, (44, 28292): 562.7373331492117, (44, 28293): 560.9607077466309, (44, 28295): 559.778676685693, (44, 28296): 560.3471719341599, (44, 28297): 559.3796071972514, (44, 28302): 558.3739280024075, (44, 28310): 588.7895639521096, (44, 28313): 590.3153280127462, (44, 28372): 591.2629882599771, (44, 28398): 591.4082108767803, (44, 28399): 590.5866953407492, (44, 28400): 591.8383539871969, (44, 28401): 588.6312271970836, (44, 28445): 588.9677170171087, (44, 28475): 586.5518576177888, (44, 28885): 65.43593720839839, (44, 28886): 65.02463116606255, (44, 28915): 67.76442204577722, (44, 28916): 66.38873172439224, (44, 28917): 66.37869908990596, (44, 28921): 66.7140333331377, (44, 28931): 66.94187828581964, (44, 28945): 70.1589621671774, (44, 28982): 68.41141398308731, (44, 29219): 86.49552272870666, (44, 29228): 82.65861846233575, (44, 29246): 115.68907821855224, (44, 29248): 117.98550441916184, (44, 29282): 111.64841949922611, (44, 29290): 115.94480180052498, (44, 29291): 115.44899243194911, (44, 29292): 116.27092432175401, (44, 29293): 113.85448760296167, (44, 29294): 116.84772941683197, (44, 29298): 114.70776617993728, (44, 29299): 115.19041159220488, (44, 29304): 111.43099162055091, (44, 29317): 104.79174139197838, (44, 29323): 104.19922988874671, (44, 29330): 107.51243884867, (44, 29331): 108.58726787463789, (44, 29344): 92.80953261422341, (44, 29445): 79.8152978187287, (44, 29724): 754.7771013075055, (44, 29738): 755.7553260147873, (44, 29745): 752.730085710965, (44, 29748): 752.4236351349863, (44, 29750): 753.6557110309293, (44, 29759): 751.189239222641, (44, 29772): 754.7908262208531, (44, 29781): 753.9795118641227, (44, 29784): 753.7360497325769, (44, 29790): 754.6104286722477, (44, 29811): 752.1739670560333, (44, 29817): 756.5592927910667, (44, 29818): 755.7543606979893, (44, 29929): 752.9295678702453, (44, 30039): 768.0579918089572, (44, 30066): 761.184673695289, (44, 30116): 726.0952869800686, (44, 30238): 674.2094142987518, (44, 30248): 702.1707409675145, (44, 30260): 702.9615027228891, (44, 30545): 44.74688965013662, (44, 30733): 24.0, (44, 30756): 41.92157636981306, (44, 30921): 24.68667651358931, (44, 31079): 161.90998751271826, (44, 31149): 157.99064528200526, (44, 31154): 159.30350664229786, (44, 31160): 158.12381749181313, (44, 31163): 159.93146131650423, (44, 31189): 174.62830064955645, (44, 31215): 174.78654189675242, (44, 31259): 182.6008657331202, (44, 31262): 183.83891752822137, (44, 31430): 165.73527821946286, (44, 31568): 219.52199407870333, (44, 31751): 173.43980097844772, (45, 109): 729.9563410051214, (45, 872): 355.85412336385167, (45, 873): 354.8188942034595, (45, 877): 353.97145761030436, (45, 879): 353.6975123746485, (45, 884): 351.99183287798365, (45, 889): 351.91759337719986, (45, 891): 352.67157255563427, (45, 892): 353.15432281735195, (45, 894): 353.79052730009147, (45, 896): 356.83414874486897, (45, 903): 352.5232555559013, (45, 909): 358.341572414854, (45, 910): 359.06558746129025, (45, 912): 359.48609132338254, (45, 913): 359.5382196841942, (45, 916): 361.2240134486345, (45, 926): 360.22968406262265, (45, 927): 360.83074107621144, (45, 948): 353.25400153936874, (45, 961): 357.5912413953964, (45, 962): 358.2715017642896, (45, 963): 358.77971831056504, (45, 967): 352.58599369091246, (45, 974): 350.2647415527947, (45, 998): 351.1606237616578, (45, 1014): 347.5949041502368, (45, 1086): 391.6409757888651, (45, 1087): 395.86699318084453, (45, 1089): 394.5401634930098, (45, 1090): 393.824575782592, (45, 1092): 392.5317886389514, (45, 1097): 392.7051086251901, (45, 1107): 394.51125000581476, (45, 1387): 615.2206610509184, (45, 1554): 633.398612805584, (45, 1827): 293.71613240019576, (45, 1828): 294.2947727647884, (45, 1829): 293.8072088926015, (45, 1830): 290.9467308431961, (45, 1831): 291.43034857932986, (45, 1832): 291.7584199384256, (45, 1833): 292.25550414923, (45, 1836): 292.8692980705562, (45, 1841): 291.86363740630327, (45, 1843): 291.9749822513245, (45, 1844): 291.4269970096079, (45, 1845): 291.1230243153451, (45, 1847): 293.0405182346688, (45, 1848): 292.70413108826284, (45, 1849): 290.660812511368, (45, 1850): 290.96560970116394, (45, 1851): 291.1143640425014, (45, 1852): 289.937284558628, (45, 1854): 290.69231017233625, (45, 1856): 291.5575756192049, (45, 1857): 292.09518662816953, (45, 1858): 291.61170537731675, (45, 1861): 292.8287576930904, (45, 1866): 290.57877205932294, (45, 1867): 292.8338372502297, (45, 1868): 293.8704753190139, (45, 1870): 289.94713050736806, (45, 1871): 293.8296565234785, (45, 1875): 291.48919684446963, (45, 1880): 292.4001730909281, (45, 1882): 290.6611332409131, (45, 1883): 292.2744309918699, (45, 1889): 294.1910348045263, (45, 1893): 295.6894026627678, (45, 1894): 296.15669834693745, (45, 1899): 295.10850690159833, (45, 1900): 295.3998196938431, (45, 1902): 295.454769742297, (45, 1905): 294.5235082407496, (45, 1907): 293.73025066156765, (45, 1910): 295.0949523886948, (45, 1917): 297.9602594783183, (45, 1920): 294.73732070225304, (45, 1935): 296.73172170028465, (45, 1937): 296.20733189812415, (45, 1946): 298.0369401692691, (45, 1949): 298.4930519737552, (45, 1950): 296.05046759748683, (45, 1951): 296.58790876614046, (45, 1952): 293.4335397665636, (45, 1953): 296.1261147702524, (45, 1954): 294.20503435138335, (45, 1958): 297.28006742177155, (45, 1960): 296.3244202663993, (45, 1968): 295.95544356575107, (45, 1969): 298.9552314834001, (45, 1974): 297.96248608394814, (45, 1975): 297.20859165919154, (45, 1979): 298.87122785821856, (45, 1980): 296.6314285119715, (45, 1981): 297.9976599159532, (45, 1985): 298.58333853025664, (45, 1994): 291.0364522268261, (45, 2011): 289.89813651942836, (45, 2019): 285.9631008848108, (45, 2020): 286.4593686735511, (45, 2029): 286.1720362911285, (45, 2030): 286.83995010672095, (45, 2032): 284.9963175840665, (45, 2033): 286.2482391434148, (45, 2034): 285.1402078845584, (45, 2036): 280.6695764060844, (45, 2037): 281.9855464269166, (45, 2038): 287.1632397632402, (45, 2042): 285.00202425912084, (45, 2050): 287.9617002107316, (45, 2051): 286.79886192078243, (45, 2053): 287.2639503991202, (45, 2054): 287.0253723942659, (45, 2066): 287.30299305483504, (45, 2067): 287.91348627762807, (45, 2071): 292.0266322618035, (45, 2072): 292.5677717274866, (45, 2073): 296.5407142594524, (45, 2074): 295.83415804980257, (45, 2080): 294.5228783636042, (45, 2082): 292.59711003706155, (45, 2083): 292.95526814229305, (45, 2089): 294.09540733781006, (45, 2090): 294.6293931407586, (45, 2092): 295.4611535878291, (45, 2098): 295.8246810966639, (45, 2099): 294.9543613889678, (45, 2101): 294.82285253161547, (45, 2102): 295.42178775923463, (45, 2103): 294.8041591360391, (45, 2104): 293.9792560848337, (45, 2106): 292.40828197791325, (45, 2112): 293.9327205345095, (45, 2113): 294.8720226912802, (45, 2114): 293.2253359971569, (45, 2117): 291.5824771385871, (45, 2123): 332.36781460242065, (45, 2124): 332.525577829349, (45, 2134): 329.3223671383502, (45, 2138): 330.88035549988086, (45, 2141): 330.2238371639491, (45, 2148): 319.73692335069455, (45, 2150): 329.35274815691025, (45, 2151): 328.7211404593373, (45, 2152): 328.54574121372747, (45, 2153): 320.8071877947216, (45, 2154): 320.8896373120349, (45, 2155): 319.01973606427185, (45, 2156): 320.2085344570879, (45, 2157): 313.7630309076152, (45, 2160): 325.93501391405607, (45, 2161): 327.4612066138683, (45, 2162): 316.7716829160207, (45, 2163): 316.9319571250728, (45, 2164): 316.26854588297164, (45, 2168): 323.9274550001598, (45, 2172): 319.1558519579591, (45, 2174): 327.3580850633123, (45, 2178): 317.8306576818374, (45, 2179): 317.33668758590903, (45, 2183): 329.6292881775782, (45, 2185): 328.9765256982935, (45, 2186): 329.2043249512074, (45, 2190): 327.1383602858061, (45, 2192): 327.31726707409047, (45, 2193): 330.04369712753527, (45, 2194): 330.2236515755866, (45, 2195): 328.83018310552444, (45, 2197): 326.58289609090804, (45, 2205): 324.8343725640034, (45, 2207): 323.0264534565156, (45, 2208): 323.75219711472243, (45, 2212): 333.1087939687939, (45, 2214): 312.54681473267095, (45, 2225): 308.27047326661256, (45, 2231): 338.462085193101, (45, 2278): 297.92835630290966, (45, 2284): 295.39013465699566, (45, 2285): 294.4934296310395, (45, 2291): 288.86584237006497, (45, 2292): 296.23472513083414, (45, 2307): 295.36985092105635, (45, 2313): 286.62243795803283, (45, 2317): 299.4617822730205, (45, 2319): 295.3998740532399, (45, 2321): 294.03504400476675, (45, 2323): 296.15015516976445, (45, 2326): 299.59043613437035, (45, 2327): 299.7081044368948, (45, 2329): 299.5739000144138, (45, 2330): 298.9280978989625, (45, 2332): 297.7371697342192, (45, 2344): 301.0797559952045, (45, 2346): 299.6195165832939, (45, 2361): 311.92098595428575, (45, 2368): 303.67085420297303, (45, 2374): 302.43883823060975, (45, 2375): 303.1488640841005, (45, 2377): 304.6019568538066, (45, 2378): 302.45425505822, (45, 2379): 300.95435049316785, (45, 2380): 301.9756126307699, (45, 2383): 305.39423630510447, (45, 2385): 305.8494893956715, (45, 2395): 307.1618649491542, (45, 2397): 300.3279996533598, (45, 2398): 304.9129883954724, (45, 2399): 305.41442096744953, (45, 2400): 305.486200694482, (45, 2402): 301.04571229952893, (45, 2403): 300.8293516590052, (45, 2404): 301.3836978558316, (45, 2405): 301.3599370593697, (45, 2407): 302.2612415204805, (45, 2408): 301.3800594628502, (45, 2409): 301.5973845364384, (45, 2411): 298.35743348167335, (45, 2412): 299.3414814739729, (45, 2413): 298.8258068943993, (45, 2414): 298.7767952553937, (45, 2422): 297.5601524213723, (45, 2424): 299.82357001683744, (45, 2426): 300.280987831847, (45, 2433): 299.6953467304796, (45, 2436): 298.1792736664745, (45, 2437): 299.8847795488095, (45, 2440): 299.94005899278864, (45, 2445): 281.9865922525596, (45, 2447): 283.8428735567167, (45, 2454): 283.4746930954831, (45, 2455): 284.65126813880516, (45, 2460): 284.29484127626023, (45, 2461): 284.06148928231295, (45, 2471): 275.44161016102163, (45, 2492): 231.0437850622672, (45, 2511): 240.1828697387132, (45, 2523): 235.30643155291546, (45, 2525): 233.01231176210058, (45, 2535): 257.1877514132922, (45, 2537): 256.68976677045293, (45, 2538): 258.218093665884, (45, 2539): 252.42921883472746, (45, 2540): 257.27012944590047, (45, 2542): 255.59603434233554, (45, 2559): 268.4312474223471, (45, 2575): 261.15098587743165, (45, 2599): 278.2119298112185, (45, 2600): 273.59529383536034, (45, 2607): 280.7177242476333, (45, 2627): 218.7150639804436, (45, 2647): 214.0954992166646, (45, 2674): 220.73878466967003, (45, 2681): 217.7610350949337, (45, 2683): 218.8391455320121, (45, 2686): 220.6780139424364, (45, 2689): 216.42143135037992, (45, 2690): 215.6809531793742, (45, 2713): 193.8713561816006, (45, 2714): 190.9178458571371, (45, 2715): 191.1477568629056, (45, 2739): 191.82868903968333, (45, 2740): 198.87572082325616, (45, 2741): 199.56970461088733, (45, 2749): 188.36123745037523, (45, 2750): 189.49338837988725, (45, 2752): 190.13469222502857, (45, 2755): 189.63762413201943, (45, 2758): 188.69150657692452, (45, 2759): 189.17054184974938, (45, 2769): 190.1309019436967, (45, 2771): 197.00363183830248, (45, 2779): 189.28823091034255, (45, 2784): 184.1013829608517, (45, 2800): 176.73754495273135, (45, 2802): 194.37768898159567, (45, 2803): 195.2886340566773, (45, 2804): 195.56648793763318, (45, 2805): 191.57972460565927, (45, 2807): 192.55427733063408, (45, 2809): 190.29482778775932, (45, 2812): 191.82492768376903, (45, 2814): 183.73688003569953, (45, 2817): 175.01684695889068, (45, 2819): 194.98800549302754, (45, 2823): 183.4085199931639, (45, 2832): 190.39445851548092, (45, 2836): 189.81773327587592, (45, 2839): 193.5512099785141, (45, 2841): 179.48506686517726, (45, 2843): 181.00460034552592, (45, 2846): 185.95880158339833, (45, 2849): 188.83471089220424, (45, 2852): 189.32125886544927, (45, 2853): 188.55189582507828, (45, 2876): 184.04992731114055, (45, 2877): 183.93417743472298, (45, 2885): 174.86593711407377, (45, 2918): 201.3646338124914, (45, 2921): 200.38705658961928, (45, 2925): 208.25257235235838, (45, 2926): 212.7597180956176, (45, 2930): 197.55151687056926, (45, 2931): 205.59717088872725, (45, 2938): 199.65227809535654, (45, 2940): 208.30758751594115, (45, 2947): 209.8139652736056, (45, 2949): 201.42691806829188, (45, 2950): 199.81530850548222, (45, 2952): 199.6853791104725, (45, 2958): 200.36471000835883, (45, 2959): 202.39515444343212, (45, 2960): 201.92578148584045, (45, 2961): 201.0631019334258, (45, 2963): 199.32142209733524, (45, 2968): 198.36799612889675, (45, 2976): 200.32541793009878, (45, 2981): 186.9468593026199, (45, 2982): 184.91130711400106, (45, 2984): 184.39351135805566, (45, 3003): 182.08311152649463, (45, 3046): 204.46163629066334, (45, 3050): 193.97227074401803, (45, 3051): 194.77309979974177, (45, 3053): 193.8294972555196, (45, 3069): 191.22342677447287, (45, 3071): 198.3866149842825, (45, 3080): 171.55377487732795, (45, 3199): 169.72712132551374, (45, 3200): 168.2334542349668, (45, 3205): 170.5357237760046, (45, 3209): 168.085875654691, (45, 3215): 169.34050225664078, (45, 3217): 168.86839606396163, (45, 3249): 170.53956788739666, (45, 3263): 175.3220724998511, (45, 3289): 174.87240681308873, (45, 3301): 172.14355887072296, (45, 3302): 173.00156081542679, (45, 3307): 173.0660575427094, (45, 3310): 172.37660261634994, (45, 3391): 118.49491085209179, (45, 3509): 349.24016661834776, (45, 3510): 350.376157755726, (45, 3511): 350.27422427651464, (45, 3512): 351.5501273956014, (45, 3514): 351.83606788055266, (45, 3519): 343.3991589429204, (45, 3536): 348.40777909540225, (45, 3545): 347.3241909748781, (45, 3548): 349.9222279601919, (45, 3572): 346.9606517297939, (45, 3581): 346.15382501095246, (45, 3583): 349.614363481665, (45, 3601): 340.2529301994929, (45, 3656): 339.7164933087877, (45, 3669): 337.06329677406006, (45, 3670): 335.7904246135442, (45, 3695): 343.9005909375286, (45, 3696): 343.14229798975106, (45, 3782): 361.8181525445323, (45, 3792): 361.04342968645005, (45, 3989): 871.709692923371, (45, 4008): 877.564752818805, (45, 4031): 874.8702756750536, (45, 4045): 874.9965261400506, (45, 4144): 877.4731764132721, (45, 4145): 873.9066625040713, (45, 4164): 875.7570011520028, (45, 4168): 875.0137914592665, (45, 4173): 875.1809847574762, (45, 4181): 871.5898362312751, (45, 4228): 865.7562182240092, (45, 4248): 867.5844039760223, (45, 4254): 845.1642759331721, (45, 4260): 844.272065327913, (45, 4262): 847.0053981406517, (45, 4273): 845.903679927396, (45, 4319): 831.4036500701868, (45, 4326): 830.5405792244657, (45, 4328): 830.5317087805585, (45, 4334): 832.492198708724, (45, 4335): 832.2004040758811, (45, 4372): 862.479437369813, (45, 4413): 886.3679682039992, (45, 4434): 861.4015053406036, (45, 4447): 864.2294764207464, (45, 4452): 861.7742463156693, (45, 4463): 814.9417054272224, (45, 4465): 816.5005201694715, (45, 4619): 889.6157734152981, (45, 4645): 894.6939646671252, (45, 4657): 893.9272325541248, (45, 4666): 891.9659384188307, (45, 4676): 895.5553941270113, (45, 4678): 896.338000866489, (45, 4689): 893.93551945292, (45, 4704): 911.7596633879728, (45, 4726): 954.4750200247877, (45, 4727): 953.6902408558407, (45, 4730): 952.1744392863869, (45, 4731): 952.5656410275351, (45, 4734): 953.6689852829313, (45, 4735): 952.8885641727115, (45, 4736): 953.232715245288, (45, 4737): 951.8688027412319, (45, 4738): 952.019416595463, (45, 4756): 952.7850424211731, (45, 4760): 949.018572334989, (45, 4761): 949.5328573090704, (45, 4762): 947.9004646464173, (45, 4765): 949.3850748788636, (45, 4773): 956.0575993623081, (45, 4774): 955.2748091332526, (45, 4790): 955.5484836154077, (45, 4795): 954.8834181531777, (45, 4799): 955.5697658736053, (45, 4801): 957.0958556834738, (45, 4804): 955.2517968817384, (45, 4805): 954.7035101744409, (45, 4806): 954.8535513517495, (45, 4815): 954.0277217636266, (45, 4816): 956.0302357157728, (45, 4817): 956.3195990141066, (45, 4826): 955.181064875166, (45, 4830): 954.0254679112511, (45, 4839): 951.3051831461247, (45, 4840): 951.9692065012006, (45, 4841): 950.2824271931528, (45, 4846): 949.7522500726841, (45, 4848): 949.4982433194027, (45, 4850): 950.199391561862, (45, 4871): 941.3994749519701, (45, 4883): 948.2385776899498, (45, 4900): 944.8207375995974, (45, 4901): 943.7855852432859, (45, 4917): 888.0377157489899, (45, 4931): 882.1937500804875, (45, 4944): 888.7597151212351, (45, 4956): 883.2062896096016, (45, 4958): 882.9186867350478, (45, 4959): 881.7276276016986, (45, 4961): 884.4376847202894, (45, 4966): 881.7097447210896, (45, 5207): 875.2218780702804, (45, 5272): 763.9286189549774, (45, 5283): 766.121981904162, (45, 5287): 769.6200372780514, (45, 5289): 770.5783285936977, (45, 5293): 764.3085823970988, (45, 5295): 770.4502531236604, (45, 5296): 770.4140927413106, (45, 5298): 770.3441870690867, (45, 5303): 772.1534356202126, (45, 5305): 762.6790225210299, (45, 5306): 760.9861351466916, (45, 5307): 761.5442939850824, (45, 5308): 763.6867158065096, (45, 5313): 763.5852115716508, (45, 5314): 764.9628490316799, (45, 5317): 763.7028663055411, (45, 5319): 770.046877398364, (45, 5324): 768.8093757813466, (45, 5326): 768.0105276286881, (45, 5348): 760.4817211590018, (45, 5351): 762.0947289711158, (45, 5399): 771.8041645951203, (45, 5413): 764.8503096532789, (45, 5422): 772.9901001460622, (45, 5445): 768.0011437644354, (45, 5448): 765.9221762008472, (45, 5456): 765.4319477334316, (45, 5467): 767.360904863312, (45, 5624): 744.4168015121284, (45, 5671): 812.1050282824459, (45, 5672): 809.2339918064224, (45, 5797): 846.1407777973144, (45, 5871): 800.5169742463623, (45, 5976): 776.2394680879576, (45, 6118): 161.5524817012113, (45, 6248): 118.9148505338222, (45, 6345): 613.1511578816202, (45, 6352): 606.1378481916043, (45, 6354): 615.075962417014, (45, 6359): 616.0882500876917, (45, 6376): 606.3444653397647, (45, 6378): 614.2014443579768, (45, 6381): 615.2561668614512, (45, 6383): 611.8129424973291, (45, 6396): 613.0154784721375, (45, 6399): 612.791195193575, (45, 6408): 606.7665286922595, (45, 6409): 611.070337995403, (45, 6419): 601.3782540625184, (45, 6422): 608.4762400086664, (45, 6423): 607.9670324575759, (45, 6424): 615.5196754257322, (45, 6439): 614.5061060078658, (45, 6464): 612.888823742022, (45, 6465): 611.8350825949796, (45, 6469): 611.9683124197024, (45, 6470): 611.3697967269891, (45, 6472): 618.3199129671647, (45, 6480): 618.5392914011665, (45, 6486): 624.5670096094667, (45, 6497): 622.6275087466348, (45, 6503): 615.515403543416, (45, 6508): 614.8230994017025, (45, 6509): 616.7143089697964, (45, 6521): 620.1945564600973, (45, 6544): 620.8361953523495, (45, 6552): 611.5430025322765, (45, 6553): 610.5738644941583, (45, 6554): 609.5729498230402, (45, 6578): 612.9999552094787, (45, 6582): 613.4398570166128, (45, 6601): 613.6949594320587, (45, 6609): 620.5654516068053, (45, 6610): 621.0963045642853, (45, 6611): 620.6720052609154, (45, 6614): 619.7728766990748, (45, 6615): 620.1760848930854, (45, 6616): 622.0485750694585, (45, 6617): 621.2958834598746, (45, 6618): 623.6269309808694, (45, 6619): 619.1570836744002, (45, 6620): 622.4634502982286, (45, 6621): 621.6774245813468, (45, 6622): 621.6071610459386, (45, 6623): 620.0998599939815, (45, 6624): 619.7337814564706, (45, 6625): 619.360809998338, (45, 6626): 618.9408726823096, (45, 6627): 619.2252344732989, (45, 6628): 622.6873269813758, (45, 6629): 620.456474095742, (45, 6630): 617.9944844176092, (45, 6632): 620.1491752590055, (45, 6634): 617.302287745237, (45, 6635): 621.1524139765713, (45, 6636): 622.233126985138, (45, 6637): 619.309007448903, (45, 6638): 618.4675585821773, (45, 6639): 619.5377954205792, (45, 6640): 618.418485057229, (45, 6641): 621.9658549671398, (45, 6642): 618.7461063508553, (45, 6643): 618.5701571331864, (45, 6645): 619.4538338098909, (45, 6646): 623.0044478040012, (45, 6647): 618.8642709272701, (45, 6653): 620.0183005283857, (45, 6655): 619.4236582325573, (45, 6658): 617.388996657018, (45, 6662): 618.9750365130812, (45, 6819): 575.2350945661495, (45, 6996): 598.8462396875346, (45, 7059): 609.9561378415576, (45, 7187): 608.7321433806006, (45, 7304): 574.615506634132, (45, 7528): 605.2418817440457, (45, 7720): 665.5825941182396, (45, 7793): 666.852091352048, (45, 7807): 666.898230644331, (45, 7808): 667.141168112636, (45, 7831): 629.6219495311747, (45, 7850): 638.5141398473568, (45, 7852): 635.4648880737925, (45, 8012): 658.7969574881714, (45, 8125): 686.7301820130052, (45, 8208): 686.7184734995309, (45, 8392): 644.7093733053333, (45, 8651): 522.0768180663358, (45, 9088): 563.181178735447, (45, 9443): 526.0587895698026, (45, 9444): 528.045745235638, (45, 9828): 496.81007293454377, (45, 9868): 480.2701399779304, (45, 10180): 689.0701851479247, (45, 10256): 718.955263494864, (45, 10276): 702.9828263565681, (45, 10378): 699.6050699208397, (45, 10676): 690.6463724214933, (45, 10714): 675.0119137446383, (45, 10730): 669.8666333825943, (45, 10862): 725.8111435739663, (45, 10881): 730.4402662412637, (45, 10883): 730.0065737681842, (45, 10885): 724.7955011188744, (45, 10891): 729.3426335730113, (45, 10909): 728.7469915739687, (45, 10911): 729.2017482470902, (45, 10913): 728.1961171269439, (45, 10915): 728.047567858163, (45, 10919): 728.6075464683734, (45, 11037): 700.0245130938225, (45, 11039): 687.3085632609793, (45, 11516): 911.4782491264833, (45, 11856): 833.1796445838692, (45, 11857): 833.2484983579399, (45, 11861): 833.2768446531376, (45, 11881): 830.690131118699, (45, 11902): 825.8390564399806, (45, 11911): 823.8842361841876, (45, 11914): 825.0284248921926, (45, 11922): 829.0065033665397, (45, 11924): 829.8731702428532, (45, 11926): 828.4121023359386, (45, 11950): 829.9817007623361, (45, 11963): 834.717968548498, (45, 11983): 829.6115990259835, (45, 11985): 837.194212673788, (45, 12009): 834.5998379901094, (45, 12010): 831.6640763552642, (45, 12018): 831.9873986985341, (45, 12020): 833.1391150257651, (45, 12021): 833.5072669706508, (45, 12024): 836.7017870791163, (45, 12025): 835.9665393120846, (45, 12027): 835.1248611475513, (45, 12031): 831.1149447139876, (45, 12032): 832.4928762785689, (45, 12035): 833.9966340364853, (45, 12041): 838.577528271055, (45, 12045): 792.6613644831547, (45, 12145): 811.2021359823395, (45, 12275): 869.6883464673421, (45, 12294): 859.016118578489, (45, 12358): 883.2861050132059, (45, 12463): 891.3231706542122, (45, 12465): 890.89113706345, (45, 12482): 897.2791293286585, (45, 12503): 896.1805164394225, (45, 12506): 897.4555839843766, (45, 12549): 896.9141470393874, (45, 12559): 895.4982953809634, (45, 12569): 895.7573240331186, (45, 12572): 896.7618004437198, (45, 12574): 894.9075670586188, (45, 12576): 898.2915776843648, (45, 12591): 899.3352175618559, (45, 12608): 908.0758385332806, (45, 12696): 896.4049508924991, (45, 12710): 905.4046744029623, (45, 12728): 900.029275263399, (45, 12766): 699.6288192919692, (45, 12771): 695.6156040564224, (45, 12790): 694.3084421018154, (45, 12795): 690.7353848098511, (45, 12797): 682.7656987510006, (45, 12798): 684.4109238563767, (45, 12811): 692.6704102354425, (45, 12830): 689.0319104533759, (45, 12848): 692.232870886723, (45, 12850): 693.989358869747, (45, 12852): 689.1616197548069, (45, 12854): 687.8766948571795, (45, 12859): 693.9733292156425, (45, 12861): 686.2231439438065, (45, 12865): 693.4806174775846, (45, 12866): 693.3325278783669, (45, 12867): 695.4502932811234, (45, 12874): 694.3507561622266, (45, 12875): 695.5458806743496, (45, 12881): 690.9591048772952, (45, 12883): 692.6118926334292, (45, 12885): 696.2755186580214, (45, 12888): 692.2121057573714, (45, 12889): 692.1881567200893, (45, 12892): 694.4298866360676, (45, 12893): 691.9176520468628, (45, 12896): 693.0446718459876, (45, 12906): 692.875357081554, (45, 13018): 672.1568158573874, (45, 13071): 670.331915280602, (45, 13131): 667.641284475165, (45, 13146): 677.9995567024466, (45, 13159): 655.7300288822612, (45, 13193): 666.5410375029369, (45, 13198): 654.6740183682657, (45, 13292): 673.1570843897435, (45, 13296): 681.7687152844504, (45, 13406): 639.5251413972359, (45, 13407): 638.578506636183, (45, 13417): 633.9363430661829, (45, 13418): 635.0445551799509, (45, 13438): 644.5340511723198, (45, 13442): 647.0359755410556, (45, 13443): 645.5807990148087, (45, 13764): 505.67673991344043, (45, 13766): 507.4880780029566, (45, 13771): 504.6016613049444, (45, 13783): 506.0670261260214, (45, 13784): 509.9486528469175, (45, 13792): 499.4407720425262, (45, 13824): 504.5978864008069, (45, 14017): 522.0470514426383, (45, 14870): 721.5254920727172, (45, 14997): 602.288378465713, (45, 15000): 603.35776868203, (45, 15003): 605.4117271106187, (45, 15006): 604.0260319380639, (45, 15007): 605.2842683885923, (45, 15056): 607.818197457444, (45, 15063): 607.3102420212499, (45, 15069): 607.9538343082891, (45, 15076): 606.1003093481897, (45, 15086): 601.2980343078871, (45, 15087): 601.290145882105, (45, 15111): 596.8986150531081, (45, 15116): 599.5112766899914, (45, 15722): 568.044393435653, (45, 15998): 572.4598196178604, (45, 16073): 241.01113531688475, (45, 16939): 270.19035572022176, (45, 16940): 271.2014650071659, (45, 16951): 266.3265929160205, (45, 16963): 267.14849902240877, (45, 16965): 267.566671673938, (45, 16969): 265.51483159277365, (45, 16970): 268.0220191621121, (45, 16971): 267.7912140908671, (45, 16973): 266.4390325326452, (45, 16974): 266.4489568385252, (45, 16976): 268.89186131220686, (45, 16978): 269.1877104434187, (45, 16980): 270.1305888461825, (45, 16982): 265.04110484796405, (45, 17045): 155.766494515792, (45, 17048): 155.5062594231577, (45, 17304): 861.7430546292107, (45, 17305): 859.2225796344485, (45, 17330): 860.7375295472366, (45, 17334): 859.7715526708324, (45, 17343): 862.1226136079771, (45, 17345): 858.2423858885638, (45, 17347): 859.638897448562, (45, 17351): 856.7606922694844, (45, 17372): 858.9768723789849, (45, 17373): 862.2134471556576, (45, 17377): 862.322073208363, (45, 17382): 859.9082629844488, (45, 17383): 860.8422045424378, (45, 17389): 859.3001797912041, (45, 17400): 861.9953957347644, (45, 17401): 862.1768454452352, (45, 17402): 861.9986185334184, (45, 17403): 862.122037259724, (45, 17440): 856.8182786932808, (45, 17455): 860.7430849654183, (45, 17491): 859.9002596597221, (45, 17507): 861.6480153742111, (45, 17509): 863.4169397640511, (45, 17590): 854.2104610440043, (45, 17615): 855.6623398110637, (45, 17642): 856.3536676763695, (45, 17643): 855.6801090441926, (45, 17668): 855.9506013094499, (45, 17721): 855.7232078967122, (45, 17754): 869.9677054956466, (45, 17769): 863.7536302098732, (45, 17776): 855.511368889649, (45, 17804): 866.3092359712381, (45, 17809): 867.737382800535, (45, 17824): 867.7165292469573, (45, 17837): 859.310244336215, (45, 17838): 858.647857372696, (45, 17862): 857.1985038626934, (45, 17866): 860.6174418256746, (45, 17872): 856.6726860450354, (45, 17873): 853.8783653287993, (45, 17881): 858.0447731031726, (45, 17947): 391.5296362462123, (45, 17951): 391.3721533992708, (45, 17953): 392.40052776627846, (45, 17954): 393.1001287761907, (45, 17959): 389.6711700209098, (45, 17963): 387.78806330955257, (45, 18000): 390.71585379804105, (45, 18001): 392.0269527245382, (45, 18111): 439.97340114215734, (45, 18148): 452.13263824141393, (45, 18166): 451.0261350097795, (45, 18189): 440.31876436214526, (45, 18239): 863.4841817234392, (45, 18240): 863.2956094743639, (45, 18245): 863.528238575885, (45, 18247): 863.0343858151153, (45, 18251): 863.3139207277426, (45, 18256): 863.4167883766979, (45, 18258): 862.9610025377704, (45, 18259): 862.9326534128238, (45, 18260): 862.9415763320729, (45, 18262): 863.085144682854, (45, 18263): 863.4124470995423, (45, 18264): 863.4323295672938, (45, 18266): 863.0376654860853, (45, 18267): 863.0812966484723, (45, 18268): 863.0384569636217, (45, 18269): 863.1070086320851, (45, 18275): 863.0738960785864, (45, 18285): 863.4933833885368, (45, 18308): 862.7536847500842, (45, 18313): 862.0185946532858, (45, 18314): 861.8197735747751, (45, 18315): 863.5794741318251, (45, 18316): 863.3375010158592, (45, 18317): 863.3550530178932, (45, 18320): 863.7055855910828, (45, 18321): 863.6111505142622, (45, 18322): 863.6857119020709, (45, 18324): 864.0755056030293, (45, 18325): 864.6279476495065, (45, 18326): 864.4327307298034, (45, 18327): 863.1782301989147, (45, 18329): 865.1336582416833, (45, 18330): 864.1399366609132, (45, 18331): 863.8837064716231, (45, 18332): 863.500708715206, (45, 18333): 864.2874862463917, (45, 18336): 864.3223044504222, (45, 18337): 864.6571481641068, (45, 18403): 863.0813547005995, (45, 18432): 848.8628529800317, (45, 18451): 858.4568494104393, (45, 18466): 868.4529080186107, (45, 18481): 864.3328458307496, (45, 18483): 864.1704551398938, (45, 18484): 863.990709534206, (45, 18485): 863.6134213172766, (45, 18486): 865.0059410927503, (45, 18487): 864.4940691349527, (45, 18489): 864.3727015176325, (45, 18490): 865.5180565107809, (45, 18491): 865.8516451991691, (45, 18492): 863.646157464232, (45, 18493): 865.0802727194186, (45, 18494): 864.1062157361267, (45, 18495): 865.2937464876635, (45, 18496): 864.8114082617918, (45, 18497): 864.5255654663134, (45, 18498): 864.0304100425942, (45, 18499): 864.4889078996789, (45, 18501): 864.4426695998087, (45, 18502): 864.1677869705308, (45, 18503): 863.7601331446002, (45, 18504): 864.7499405028018, (45, 18506): 864.9508210190157, (45, 18507): 864.7803512309789, (45, 18508): 864.5818976790699, (45, 18509): 864.7410921882346, (45, 18510): 863.9933805077586, (45, 18511): 865.4985897532264, (45, 18512): 864.8436296055817, (45, 18515): 865.007513044169, (45, 18516): 865.5619401413129, (45, 18517): 865.4456106280982, (45, 18518): 865.6640951556296, (45, 18519): 864.7205752436491, (45, 18520): 864.3015470260896, (45, 18522): 865.6722940559044, (45, 18523): 865.9168452662519, (45, 18532): 866.5978788175722, (45, 18535): 865.3642075661731, (45, 18537): 864.6775468133973, (45, 18539): 864.9130996199497, (45, 18540): 865.0902573009978, (45, 18541): 865.5086340282467, (45, 18542): 865.7575211890304, (45, 18543): 864.5932096189504, (45, 18546): 865.4449368485879, (45, 18555): 866.5380017598228, (45, 18556): 866.8566425523331, (45, 18565): 866.7548073706199, (45, 18567): 867.4189840454782, (45, 18568): 866.6755072318182, (45, 18577): 870.877087659646, (45, 18583): 869.688566741042, (45, 18605): 869.9911626831978, (45, 18608): 868.4826327725335, (45, 18616): 873.9514097237382, (45, 18618): 877.6319176505425, (45, 18625): 875.1944323022586, (45, 18645): 871.6975486449982, (45, 18646): 872.8949925903929, (45, 18653): 871.3193796544284, (45, 18654): 874.0751670268231, (45, 18655): 872.5270303263254, (45, 18666): 881.2963161230471, (45, 18837): 850.4445881069363, (45, 18974): 854.3424756873907, (45, 18999): 854.9747616615635, (45, 19000): 855.9319611831751, (45, 19174): 799.5295463360088, (45, 19342): 815.3771405045567, (45, 19455): 814.6061747178798, (45, 19555): 762.9724206106789, (45, 19564): 761.5606451604443, (45, 19573): 760.4643865464242, (45, 19586): 760.2463232465195, (45, 19605): 761.6559364663044, (45, 19611): 762.5560033541844, (45, 19614): 763.2820198825552, (45, 19641): 783.5006514258963, (45, 19702): 781.8439844181846, (45, 19713): 780.6281926242893, (45, 19731): 761.5127490158279, (45, 19819): 804.7763693055593, (45, 19893): 807.5273827616878, (45, 19899): 820.5507225740155, (45, 19929): 810.3801475921535, (45, 19951): 834.2871343184792, (45, 19962): 813.4131524605103, (45, 19970): 816.471329171361, (45, 19971): 817.08992269976, (45, 19972): 815.4483599431205, (45, 19975): 814.14538247811, (45, 19978): 837.1343636036505, (45, 19987): 837.2184813789468, (45, 19989): 830.6586113178283, (45, 20039): 838.2666790351013, (45, 20043): 840.5585433119273, (45, 20047): 838.0638227973665, (45, 20052): 831.1718217133131, (45, 20054): 831.9573068203658, (45, 20085): 861.8480549013475, (45, 20104): 863.8016655818865, (45, 20132): 852.2861346191416, (45, 20203): 810.7862222924733, (45, 20280): 809.5275722337009, (45, 20285): 809.4368650017128, (45, 20290): 810.3900784461263, (45, 20297): 808.0850015548618, (45, 20309): 842.1559319855978, (45, 20453): 872.7584280325951, (45, 20485): 793.7179896326803, (45, 20520): 787.8054284644221, (45, 20526): 787.1922030657012, (45, 20698): 437.2369507077896, (45, 20868): 371.1528153927535, (45, 21042): 714.7774685276623, (45, 21057): 725.9510058102718, (45, 21066): 721.4920013316442, (45, 21075): 717.9130189201505, (45, 21093): 717.0466277561387, (45, 21098): 727.072253216979, (45, 21127): 716.456862009814, (45, 21130): 719.2677121238454, (45, 21144): 717.603315344762, (45, 21146): 715.718367121709, (45, 21147): 717.0124976955757, (45, 21148): 719.4337846986517, (45, 21153): 709.5266980957819, (45, 21293): 735.2313560110282, (45, 21426): 719.4635172709831, (45, 21442): 729.1629518435193, (45, 21451): 730.1605453055835, (45, 21466): 724.9611132777694, (45, 21469): 727.0290818482318, (45, 21471): 723.8846370526775, (45, 21473): 725.7502315841756, (45, 21475): 724.254410646663, (45, 21482): 727.8152659386, (45, 21484): 727.6588707777038, (45, 21488): 726.3043247684799, (45, 21494): 724.9657480065631, (45, 21498): 726.3216617261232, (45, 21500): 724.7475778364089, (45, 21514): 731.2630275444047, (45, 21537): 725.9529740341401, (45, 21662): 734.860828101205, (45, 21691): 727.3902811204429, (45, 21757): 708.6445712014444, (45, 21777): 697.5848725730385, (45, 21778): 695.7273294016103, (45, 21779): 697.4365730147252, (45, 21790): 698.9512348903369, (45, 21802): 700.1658162700545, (45, 21824): 702.7622817989994, (45, 21874): 698.7425781613283, (45, 21879): 698.880653035863, (45, 21983): 699.9451777682173, (45, 22002): 724.5520271430836, (45, 22132): 696.4175044085822, (45, 22261): 521.3416491136339, (45, 22298): 527.1321764745564, (45, 22339): 522.5738515233927, (45, 22508): 545.2119373929663, (45, 22841): 24.0, (45, 22842): 24.0, (45, 22874): 24.0, (45, 22941): 24.0, (45, 22956): 24.0, (45, 22960): 24.0, (45, 22968): 24.0, (45, 22970): 24.0, (45, 22974): 24.0, (45, 22980): 24.05275107325307, (45, 23025): 36.25312476545175, (45, 23028): 38.603629161240896, (45, 23081): 56.837079613472426, (45, 23104): 77.3472624233248, (45, 23147): 41.99525454818806, (45, 23298): 767.64487153518, (45, 23376): 762.5264655807784, (45, 23381): 762.6147661457666, (45, 23529): 773.4899813391625, (45, 23556): 770.1234509863813, (45, 23718): 761.8789949928287, (45, 24001): 797.4309220003354, (45, 24094): 812.3491486592598, (45, 24129): 817.4953363005806, (45, 24174): 808.95601763289, (45, 24235): 821.8181469474958, (45, 24259): 825.3332318369884, (45, 24260): 825.1793409950893, (45, 24261): 823.8674528684618, (45, 24305): 830.6354134953865, (45, 24306): 831.9233325740429, (45, 24307): 830.249066576801, (45, 24308): 806.5983436239932, (45, 24498): 839.3820028418804, (45, 24499): 839.5993826547208, (45, 24500): 838.528823853864, (45, 24668): 826.4719024964076, (45, 24711): 848.300772776138, (45, 24756): 853.8316083371444, (45, 24788): 854.4708652048924, (45, 24809): 850.7140025166292, (45, 24813): 851.7088935826105, (45, 24821): 851.300305528962, (45, 24825): 851.9565398243851, (45, 24832): 850.1772666183975, (45, 24833): 850.9536433249627, (45, 24835): 851.8344039764751, (45, 24837): 852.8181193410409, (45, 24840): 850.1867114560105, (45, 24841): 851.1177990397719, (45, 24844): 850.3977538680778, (45, 24845): 850.4185632949573, (45, 24846): 851.3175471607881, (45, 24849): 851.8251057170648, (45, 24850): 852.1605384849586, (45, 24863): 840.1031567263736, (45, 24866): 841.4229914762844, (45, 24885): 843.6507274971304, (45, 24886): 844.1522353897351, (45, 24889): 845.8083962945286, (45, 24903): 846.3748282710087, (45, 24909): 840.4111371869559, (45, 24999): 895.5509117895391, (45, 25019): 892.4447431416221, (45, 25028): 895.0812949151791, (45, 25137): 819.7667736187468, (45, 25145): 821.8284099115104, (45, 25208): 850.9264316513393, (45, 25233): 848.2702863449227, (45, 25371): 816.2835925586952, (45, 25377): 809.2348220748823, (45, 25828): 699.4698668111497, (45, 25851): 679.960603835731, (45, 25874): 696.5560400761343, (45, 25898): 706.6061682713739, (45, 25946): 697.6036128592378, (45, 26047): 737.7000213895735, (45, 26066): 763.1325210088809, (45, 26197): 744.5172062497143, (45, 26212): 658.1567791247438, (45, 26253): 654.1597537975084, (45, 26254): 655.326304788517, (45, 26257): 657.8593727201016, (45, 26258): 655.2908279942172, (45, 26260): 656.5260981068047, (45, 26266): 652.3986654225824, (45, 26267): 654.2685089179766, (45, 26271): 654.64011095744, (45, 26304): 667.8401751171219, (45, 26305): 666.896557189342, (45, 26363): 697.8608009653702, (45, 26441): 572.7422955954805, (45, 26442): 572.1130135648, (45, 26450): 573.6609162202225, (45, 26459): 577.5435312367716, (45, 26462): 579.0012377314717, (45, 26467): 575.2659740843952, (45, 26471): 574.3735767626114, (45, 26472): 573.9213946718584, (45, 26473): 573.4202007889535, (45, 26476): 568.4371800936111, (45, 26485): 575.0129735521409, (45, 26493): 573.0293059791832, (45, 26524): 580.1215202752834, (45, 26525): 579.2343091116368, (45, 26556): 575.0653366696278, (45, 26560): 578.3652602144548, (45, 26561): 579.9053680241154, (45, 26564): 574.547568076082, (45, 26569): 579.0572931431994, (45, 26570): 578.1753675130519, (45, 26573): 576.2796048422807, (45, 26581): 574.8100412164491, (45, 26583): 576.0253475398387, (45, 26593): 572.9038018091697, (45, 26837): 573.4699910429188, (45, 26844): 573.3421916501535, (45, 26863): 569.9378423668529, (45, 26893): 567.9839943075644, (45, 26902): 567.6730382590879, (45, 26905): 571.3249671819447, (45, 26912): 570.0302489964118, (45, 26921): 569.2240447819049, (45, 26922): 564.703120705116, (45, 27212): 648.0763560347962, (45, 27218): 651.5185694269634, (45, 27239): 647.1391928672531, (45, 27257): 646.0954649448466, (45, 27274): 646.433075622618, (45, 27279): 645.1683943658336, (45, 27282): 645.3866427217729, (45, 27283): 647.7905836588317, (45, 27285): 645.5690121777476, (45, 27286): 643.5209433572353, (45, 27290): 645.3694799180546, (45, 27295): 647.4156073296995, (45, 27300): 646.9049928842466, (45, 27344): 641.7221746948032, (45, 27366): 640.1957943877666, (45, 27383): 642.8514417243123, (45, 27398): 645.748419636603, (45, 27406): 646.8845146839949, (45, 27407): 647.8583416517617, (45, 27426): 656.7998451767695, (45, 27432): 654.979862651708, (45, 27460): 657.2689795122606, (45, 27523): 620.0601502273925, (45, 27545): 639.8592744205846, (45, 27602): 628.9068271633078, (45, 27606): 630.5879298720919, (45, 27646): 608.696332003123, (45, 27667): 606.5976530080727, (45, 27672): 607.5123393897405, (45, 27674): 607.224632279469, (45, 27688): 610.9569342676205, (45, 27692): 605.9946371453605, (45, 27693): 606.083487919978, (45, 27705): 604.9377211486135, (45, 27712): 603.910266285345, (45, 27786): 670.7766240506527, (45, 27790): 684.8815855822581, (45, 27791): 686.9120013196329, (45, 27795): 669.5229203377622, (45, 27801): 678.7543688820962, (45, 27813): 669.1551511387279, (45, 27816): 671.9854635775858, (45, 27823): 679.2297247639726, (45, 27830): 675.237129882783, (45, 27884): 601.0147845138257, (45, 27885): 607.8350760146783, (45, 27896): 604.2497732241192, (45, 27919): 605.0880050337948, (45, 27922): 604.3138170688383, (45, 27930): 603.4153643084037, (45, 27934): 602.697985152411, (45, 27935): 601.7734848195461, (45, 27948): 574.8159285552862, (45, 27951): 592.4533027141472, (45, 28061): 460.50569753467886, (45, 28290): 457.80183678705566, (45, 28292): 452.5989039246086, (45, 28293): 456.3773540311267, (45, 28295): 453.118642994192, (45, 28296): 456.05142342639175, (45, 28297): 460.1995452414189, (45, 28302): 457.2625829626046, (45, 28310): 222.9881974897515, (45, 28313): 217.51968282968767, (45, 28372): 225.34528990707003, (45, 28398): 224.5849699143392, (45, 28399): 224.60497597421661, (45, 28400): 223.48654351390175, (45, 28401): 227.463452164789, (45, 28445): 216.09165124642246, (45, 28475): 235.62309328546888, (45, 28885): 828.4910637153642, (45, 28886): 827.7394447945024, (45, 28915): 829.6345871253096, (45, 28916): 828.4542669402122, (45, 28917): 828.12973998652, (45, 28921): 830.1418284655919, (45, 28931): 830.1422482666695, (45, 28945): 828.5953099685669, (45, 28982): 828.6792077525063, (45, 29219): 839.9017700392986, (45, 29228): 835.0676862622668, (45, 29246): 869.0723889542842, (45, 29248): 869.6234013315042, (45, 29282): 862.7702457919567, (45, 29290): 871.2965735858635, (45, 29291): 870.2435320858652, (45, 29292): 871.3723648544127, (45, 29293): 868.742537413774, (45, 29294): 871.2557224994786, (45, 29298): 869.2040583399057, (45, 29299): 869.245264699448, (45, 29304): 866.2004230092407, (45, 29317): 859.5419263544658, (45, 29323): 858.9946379385034, (45, 29330): 862.248987205488, (45, 29331): 863.6417434460838, (45, 29344): 842.4871237354866, (45, 29445): 791.6316700206269, (45, 29724): 44.73855153828586, (45, 29738): 44.47583943253661, (45, 29745): 46.90024414412563, (45, 29748): 54.88534925930389, (45, 29750): 57.919743478645174, (45, 29759): 54.26823173224423, (45, 29772): 53.43531298711447, (45, 29781): 53.83315422457258, (45, 29784): 50.46064767122515, (45, 29790): 55.115154726053, (45, 29811): 59.173423371818004, (45, 29817): 79.46259987270564, (45, 29818): 79.91253543291569, (45, 29929): 41.94588022880968, (45, 30039): 24.0, (45, 30066): 24.0, (45, 30116): 45.33797194491391, (45, 30238): 103.20841433577945, (45, 30248): 64.19313843139435, (45, 30260): 62.93878089739498, (45, 30545): 808.9007567997954, (45, 30733): 756.2296952786133, (45, 30756): 749.9825994734789, (45, 30921): 771.4237418907236, (45, 31079): 604.9801604049552, (45, 31149): 606.8570543862648, (45, 31154): 605.6745118142766, (45, 31160): 606.699634513417, (45, 31163): 605.0128160043507, (45, 31189): 590.5500538291404, (45, 31215): 590.1628743259262, (45, 31259): 582.114652783882, (45, 31262): 580.8928890648139, (45, 31430): 602.8857246197892, (45, 31568): 545.3312856860118, (45, 31751): 592.8341682705013, (47, 109): 661.820764588238, (47, 872): 213.1036089006418, (47, 873): 211.58586164509163, (47, 877): 210.9812123430747, (47, 879): 210.64154259282824, (47, 884): 209.57404522887288, (47, 889): 209.15907428664238, (47, 891): 210.39937427114668, (47, 892): 209.71216902484588, (47, 894): 210.3841756785659, (47, 896): 213.78912675669812, (47, 903): 209.58740940736308, (47, 909): 216.0238287878157, (47, 910): 216.4944726027973, (47, 912): 217.24959591831782, (47, 913): 217.69654622011168, (47, 916): 219.45954603534756, (47, 926): 217.42584031847426, (47, 927): 218.17516545686078, (47, 948): 211.15065845659117, (47, 961): 214.93859044043782, (47, 962): 215.52356666134892, (47, 963): 215.93851316898002, (47, 967): 209.41899618251435, (47, 974): 207.5111911875882, (47, 998): 207.85350967772212, (47, 1014): 195.44535290319286, (47, 1086): 248.62515360876915, (47, 1087): 252.77364167161574, (47, 1089): 251.92107153931477, (47, 1090): 251.0307945358541, (47, 1092): 249.10837549146305, (47, 1097): 249.787822138869, (47, 1107): 250.7019273251553, (47, 1387): 542.1564756403701, (47, 1554): 567.9082676510245, (47, 1827): 139.16210998047734, (47, 1828): 139.7495222705699, (47, 1829): 139.28528043896455, (47, 1830): 136.427163412781, (47, 1831): 136.91871767591562, (47, 1832): 137.23003417089734, (47, 1833): 137.72475186356684, (47, 1836): 138.31919320102446, (47, 1841): 137.40735947753492, (47, 1843): 137.4804728238584, (47, 1844): 136.95364971053513, (47, 1845): 136.6087723832782, (47, 1847): 138.39061414839102, (47, 1848): 138.09499896192608, (47, 1849): 136.29456414184415, (47, 1850): 136.62395333110356, (47, 1851): 136.54838993304008, (47, 1852): 135.38322765604397, (47, 1854): 136.1542110659678, (47, 1856): 136.9110857323973, (47, 1857): 137.48730339003373, (47, 1858): 137.2106992823885, (47, 1861): 138.31182155561177, (47, 1866): 135.93566092105078, (47, 1867): 138.3714014573921, (47, 1868): 139.36956017690713, (47, 1870): 135.48272828756873, (47, 1871): 139.351616872631, (47, 1875): 136.94267889189138, (47, 1880): 137.77255097455793, (47, 1882): 136.05652340441122, (47, 1883): 137.92088608471323, (47, 1889): 139.57249215243894, (47, 1893): 141.15492776431714, (47, 1894): 141.58779571932158, (47, 1899): 140.46053633523167, (47, 1900): 140.76961941229706, (47, 1902): 140.97959003042166, (47, 1905): 140.1028552563377, (47, 1907): 139.1420315554505, (47, 1910): 140.51116214262873, (47, 1917): 143.6068987610605, (47, 1920): 140.14494199394068, (47, 1935): 142.29624467991223, (47, 1937): 141.81740013641695, (47, 1946): 143.32048860400707, (47, 1949): 143.80178054163935, (47, 1950): 141.28133824127679, (47, 1951): 141.8568746888459, (47, 1952): 138.75308576709767, (47, 1953): 141.44755322893246, (47, 1954): 139.5132332732945, (47, 1958): 142.58704898385494, (47, 1960): 141.68877144376015, (47, 1968): 141.34464905558139, (47, 1969): 144.50761178574044, (47, 1974): 143.47083160246078, (47, 1975): 142.72299491819166, (47, 1979): 144.28023341334276, (47, 1980): 142.04974751098644, (47, 1981): 143.43157289458708, (47, 1985): 144.0343565240645, (47, 1994): 136.2553025313308, (47, 2011): 135.29713386025892, (47, 2019): 131.80134425296538, (47, 2020): 132.2269696501238, (47, 2029): 131.72708074472004, (47, 2030): 132.56048910472296, (47, 2032): 130.5305879464624, (47, 2033): 131.87692468592022, (47, 2034): 130.77862114994886, (47, 2036): 126.15120794450257, (47, 2037): 127.50396839552391, (47, 2038): 132.65376452927728, (47, 2042): 131.27507669227748, (47, 2050): 133.54506893050709, (47, 2051): 132.3848801750829, (47, 2053): 132.86160759063148, (47, 2054): 132.68160636034065, (47, 2066): 132.84562370623792, (47, 2067): 133.45089634733318, (47, 2071): 137.20267965200188, (47, 2072): 137.7812535933117, (47, 2073): 141.66910191889414, (47, 2074): 140.96140371611955, (47, 2080): 139.6436570125384, (47, 2082): 137.83562432413993, (47, 2083): 138.21912146232523, (47, 2089): 139.3021971520765, (47, 2090): 139.85564838304668, (47, 2092): 140.65668913386972, (47, 2098): 140.94478090083203, (47, 2099): 140.07752384652719, (47, 2101): 139.94288228526923, (47, 2102): 140.5812281160407, (47, 2103): 139.94400062733044, (47, 2104): 139.1116435333307, (47, 2106): 137.69436433816918, (47, 2112): 139.0541104798452, (47, 2113): 140.0443962801552, (47, 2114): 138.42615456309738, (47, 2117): 136.8978365414056, (47, 2123): 177.48944624875824, (47, 2124): 177.64560228816455, (47, 2134): 174.4501555812705, (47, 2138): 176.00032392527086, (47, 2141): 175.35036109058197, (47, 2148): 164.85729600297307, (47, 2150): 174.4981174648703, (47, 2151): 173.85570169176796, (47, 2152): 173.69620188784018, (47, 2153): 165.9278737753585, (47, 2154): 166.0238020158712, (47, 2155): 164.15607819036356, (47, 2156): 165.35416825982733, (47, 2157): 158.892139937934, (47, 2160): 171.0608945552778, (47, 2161): 172.61208847697148, (47, 2162): 161.8944848677692, (47, 2163): 162.05191903877866, (47, 2164): 161.38850689545652, (47, 2168): 169.06218670647408, (47, 2172): 164.28035716649723, (47, 2174): 172.49214780704455, (47, 2178): 162.9516505418812, (47, 2179): 162.45945467199428, (47, 2183): 174.7493013707134, (47, 2185): 174.09665143551118, (47, 2186): 174.3245162459049, (47, 2190): 172.26428595325882, (47, 2192): 172.43795578297951, (47, 2193): 175.1638748507103, (47, 2194): 175.3448860264888, (47, 2195): 173.95143896482588, (47, 2197): 171.70458863048034, (47, 2205): 169.95474326566404, (47, 2207): 168.15736711702306, (47, 2208): 168.87528847721921, (47, 2212): 178.22892782556158, (47, 2214): 158.58348871291037, (47, 2225): 154.0748724399199, (47, 2231): 184.76568123453205, (47, 2278): 143.11330284043754, (47, 2284): 140.52649645053694, (47, 2285): 139.63351795988544, (47, 2291): 134.12253093942482, (47, 2292): 141.48312543278644, (47, 2307): 140.53219143919497, (47, 2313): 131.89860274797124, (47, 2317): 144.78623083976544, (47, 2319): 140.61931048449438, (47, 2321): 139.22096611813282, (47, 2323): 141.3428447679361, (47, 2326): 144.71586153923673, (47, 2327): 144.84372672215994, (47, 2329): 144.71924990933346, (47, 2330): 144.0867844801592, (47, 2332): 142.86893175754028, (47, 2344): 146.26174490215982, (47, 2346): 144.80055164055238, (47, 2361): 157.13294638439922, (47, 2368): 148.88250670606942, (47, 2374): 147.6921595754323, (47, 2375): 148.41273429998242, (47, 2377): 149.75413683974827, (47, 2378): 147.7493043271575, (47, 2379): 146.261590181747, (47, 2380): 147.29398845291826, (47, 2383): 150.5653382926061, (47, 2385): 151.03345505114743, (47, 2395): 152.34380296340998, (47, 2397): 145.6189491810451, (47, 2398): 150.0466794297167, (47, 2399): 150.56792142585687, (47, 2400): 150.6341937255957, (47, 2402): 146.256353549126, (47, 2403): 146.06892302807591, (47, 2404): 146.62881501683216, (47, 2405): 146.5420888809751, (47, 2407): 147.48963568108655, (47, 2408): 146.64850021816338, (47, 2409): 146.7956136137868, (47, 2411): 143.6070076499415, (47, 2412): 144.57891913520785, (47, 2413): 144.09152962159203, (47, 2414): 144.00138727217566, (47, 2422): 142.8034776551248, (47, 2424): 145.06764118402094, (47, 2426): 145.5298757743075, (47, 2433): 144.89426264630697, (47, 2436): 143.37078008801836, (47, 2437): 145.00474828869517, (47, 2440): 145.0635335442896, (47, 2445): 128.99799865093829, (47, 2447): 130.41351354720217, (47, 2454): 130.41796636005645, (47, 2455): 131.5818146491554, (47, 2460): 130.24207262630682, (47, 2461): 130.11439125217322, (47, 2471): 124.40753486583557, (47, 2492): 78.23048995416629, (47, 2511): 85.86085590576023, (47, 2523): 81.61669633215568, (47, 2525): 79.17199569535848, (47, 2535): 103.2284701538788, (47, 2537): 102.53042533936043, (47, 2538): 104.17690280963441, (47, 2539): 98.41088119855722, (47, 2540): 103.41160620037623, (47, 2542): 101.94520154349664, (47, 2559): 119.79082413007998, (47, 2575): 112.44848514804016, (47, 2599): 123.33428670706988, (47, 2600): 119.03090816527703, (47, 2607): 125.89671123746483, (47, 2627): 65.6070989082633, (47, 2647): 62.49802712714317, (47, 2674): 68.11437613685649, (47, 2681): 65.08723538730861, (47, 2683): 66.7435904461807, (47, 2686): 67.80950797237075, (47, 2689): 77.76091005249626, (47, 2690): 77.31089631763467, (47, 2713): 68.26721255151745, (47, 2714): 67.34571955623574, (47, 2715): 68.14688988799941, (47, 2739): 67.83911630931605, (47, 2740): 67.423110867268, (47, 2741): 68.13274336589096, (47, 2749): 65.3268093370394, (47, 2750): 66.04098018028509, (47, 2752): 66.82624705532488, (47, 2755): 67.16717193005121, (47, 2758): 66.59967226004994, (47, 2759): 66.80526502510342, (47, 2769): 66.40481643045494, (47, 2771): 67.36017678204107, (47, 2779): 63.63091532289008, (47, 2784): 53.32419663354024, (47, 2800): 51.637491259280644, (47, 2802): 63.651726498702324, (47, 2803): 63.9213755119844, (47, 2804): 63.66163389045565, (47, 2805): 62.70311107422111, (47, 2807): 63.17026845628911, (47, 2809): 61.756834478383794, (47, 2812): 58.39198449440249, (47, 2814): 58.47548914067172, (47, 2817): 55.53320754986221, (47, 2819): 64.5699642607438, (47, 2823): 54.407753191563806, (47, 2832): 62.94145699857955, (47, 2836): 59.618389123747576, (47, 2839): 63.692376606720636, (47, 2841): 57.148416671079744, (47, 2843): 57.456378869038886, (47, 2846): 58.31782123977313, (47, 2849): 62.67692448054697, (47, 2852): 62.20060175669817, (47, 2853): 62.874135999946404, (47, 2876): 61.27122590711291, (47, 2877): 63.91163502697388, (47, 2885): 62.058747884602376, (47, 2918): 68.60109757927044, (47, 2921): 68.94100599895853, (47, 2925): 70.007322146753, (47, 2926): 72.12528598414083, (47, 2930): 64.69672759863309, (47, 2931): 68.50556000733759, (47, 2938): 67.57984955635398, (47, 2940): 75.53587812291482, (47, 2947): 73.65663315572327, (47, 2949): 67.05264783963882, (47, 2950): 66.45679993045539, (47, 2952): 65.9239049330784, (47, 2958): 66.25830744616277, (47, 2959): 67.96625892760348, (47, 2960): 68.65691381909548, (47, 2961): 67.6435686162068, (47, 2963): 65.22807734480698, (47, 2968): 64.93212462329268, (47, 2976): 65.73745142786393, (47, 2981): 48.62221136691482, (47, 2982): 47.11143348175094, (47, 2984): 46.31657596290276, (47, 3003): 44.08297635171618, (47, 3046): 55.912233885490224, (47, 3050): 50.80796589111426, (47, 3051): 51.71024938169337, (47, 3053): 50.15264616951932, (47, 3069): 53.52913199682228, (47, 3071): 53.46668062070977, (47, 3080): 61.41132218236726, (47, 3199): 36.19851159875933, (47, 3200): 34.24115972326609, (47, 3205): 43.724202553248105, (47, 3209): 34.92261247454053, (47, 3215): 34.75032064596445, (47, 3217): 32.86443965719103, (47, 3249): 35.39231655106134, (47, 3263): 49.925044100533874, (47, 3289): 41.19563683325135, (47, 3301): 40.44319287017031, (47, 3302): 40.18832307351054, (47, 3307): 39.47480322553903, (47, 3310): 41.257917945532505, (47, 3391): 54.70629017194653, (47, 3509): 281.07298587866813, (47, 3510): 282.4471698349581, (47, 3511): 281.75385107205585, (47, 3512): 282.8018330546364, (47, 3514): 282.6974908471589, (47, 3519): 276.8384453646693, (47, 3536): 279.04849278018, (47, 3545): 277.13666768209134, (47, 3548): 279.5540052207143, (47, 3572): 277.9915303729119, (47, 3581): 278.9423615574007, (47, 3583): 280.76589221809513, (47, 3601): 273.9557301842916, (47, 3656): 275.5424861255245, (47, 3669): 277.1547847787416, (47, 3670): 275.8705761564271, (47, 3695): 283.3878285842835, (47, 3696): 282.4218732496084, (47, 3782): 284.24822517320774, (47, 3792): 284.8166160098844, (47, 3989): 860.7586879268372, (47, 4008): 867.4778999350261, (47, 4031): 865.6637474433032, (47, 4045): 864.5920765419274, (47, 4144): 866.2342421219101, (47, 4145): 860.8422326791333, (47, 4164): 863.9593746849615, (47, 4168): 862.4983226588407, (47, 4173): 862.3863064339307, (47, 4181): 858.2732784078629, (47, 4228): 852.9534877521281, (47, 4248): 853.1987024304755, (47, 4254): 821.7112110981282, (47, 4260): 821.2959847367189, (47, 4262): 824.04779285649, (47, 4273): 823.1716516807649, (47, 4319): 803.2036174668655, (47, 4326): 802.3412704144438, (47, 4328): 802.5028290138495, (47, 4334): 804.2988941098923, (47, 4335): 803.8436526648272, (47, 4372): 790.2373299051281, (47, 4413): 812.2411619633735, (47, 4434): 789.4959554575263, (47, 4447): 793.1311921993058, (47, 4452): 789.7121759203878, (47, 4463): 738.6466966212057, (47, 4465): 740.5145524953513, (47, 4619): 812.5710957288655, (47, 4645): 818.1876231067583, (47, 4657): 817.0504613637263, (47, 4666): 814.7338354918594, (47, 4676): 818.4035957352074, (47, 4678): 819.3713797741847, (47, 4689): 816.4952414922906, (47, 4704): 834.6559101579671, (47, 4726): 870.8463109475954, (47, 4727): 870.1472143730452, (47, 4730): 868.8206816475481, (47, 4731): 869.0070835401818, (47, 4734): 870.8787531547148, (47, 4735): 870.0496386354685, (47, 4736): 870.2397863029357, (47, 4737): 868.8668276138213, (47, 4738): 868.9070051744006, (47, 4756): 869.5176014782753, (47, 4760): 866.8200008159698, (47, 4761): 867.5421580443978, (47, 4762): 865.6643488325252, (47, 4765): 867.0673024769444, (47, 4773): 872.3860761728321, (47, 4774): 871.4710707450215, (47, 4790): 871.9649487816145, (47, 4795): 871.426795281798, (47, 4799): 871.6189753801737, (47, 4801): 872.6830006542218, (47, 4804): 872.0275393532341, (47, 4805): 871.5806765699059, (47, 4806): 870.7755498808623, (47, 4815): 869.8486510904308, (47, 4816): 871.7325091959153, (47, 4817): 871.7413980348518, (47, 4826): 870.8027310630852, (47, 4830): 869.6660224626029, (47, 4839): 868.843603368175, (47, 4840): 869.3269884668163, (47, 4841): 867.736735173005, (47, 4846): 867.3071447143576, (47, 4848): 866.8633570143795, (47, 4850): 867.4508551964713, (47, 4871): 860.6171530134012, (47, 4883): 866.4431254579086, (47, 4900): 863.8423424796862, (47, 4901): 862.7463061495582, (47, 4917): 806.8501565290356, (47, 4931): 801.393849436868, (47, 4944): 807.684342270701, (47, 4956): 802.1792404463275, (47, 4958): 801.5947956923227, (47, 4959): 800.2663188784647, (47, 4961): 803.4581186440208, (47, 4966): 800.5987184413962, (47, 5207): 794.5087626272684, (47, 5272): 702.5903220761829, (47, 5283): 704.4780929020193, (47, 5287): 706.6401491805116, (47, 5289): 707.4350493366895, (47, 5293): 703.7593024248729, (47, 5295): 709.1662583316682, (47, 5296): 708.6132103208876, (47, 5298): 708.2613065316007, (47, 5303): 709.4129684800529, (47, 5305): 700.4735825671329, (47, 5306): 698.2413490871843, (47, 5307): 699.4308919641473, (47, 5308): 701.1894762114979, (47, 5313): 701.7607712213477, (47, 5314): 703.1701702291164, (47, 5317): 700.8624116412606, (47, 5319): 707.4290529488711, (47, 5324): 706.7359411572303, (47, 5326): 706.3192238540987, (47, 5348): 697.346433095052, (47, 5351): 698.035284289493, (47, 5399): 707.7609705053882, (47, 5413): 699.317454739005, (47, 5422): 709.3227990019105, (47, 5445): 704.6804533512562, (47, 5448): 702.8340362369879, (47, 5456): 701.8471467863029, (47, 5467): 703.4149664557175, (47, 5624): 684.8742283381981, (47, 5671): 751.8848409021437, (47, 5672): 749.4037116167846, (47, 5797): 781.8073156156397, (47, 5871): 728.6767701119915, (47, 5976): 706.6662821169904, (47, 6118): 120.62992869874773, (47, 6248): 117.66743719371746, (47, 6345): 588.8396929221781, (47, 6352): 582.249422402171, (47, 6354): 590.463787068535, (47, 6359): 591.7446171674009, (47, 6376): 583.2612759085753, (47, 6378): 589.6793132273597, (47, 6381): 591.19197625999, (47, 6383): 587.4493061151807, (47, 6396): 590.3983273555183, (47, 6399): 588.9007911153384, (47, 6408): 582.50525339158, (47, 6409): 585.6742030381492, (47, 6419): 575.1441123863725, (47, 6422): 583.4185931540584, (47, 6423): 582.8898673230816, (47, 6424): 589.9010576558358, (47, 6439): 588.6636534482585, (47, 6464): 586.864150017189, (47, 6465): 586.1713081716889, (47, 6469): 586.9343308784142, (47, 6470): 586.517749001236, (47, 6472): 593.9706587626379, (47, 6480): 592.7341247412581, (47, 6486): 596.904402521653, (47, 6497): 595.5066137834945, (47, 6503): 587.5865860011681, (47, 6508): 587.8832023140952, (47, 6509): 589.2404836577217, (47, 6521): 593.6490112615412, (47, 6544): 593.3516584400169, (47, 6552): 584.7452435888708, (47, 6553): 583.7318099997212, (47, 6554): 582.6987143791936, (47, 6578): 586.4178510900487, (47, 6582): 585.8281470428053, (47, 6601): 586.9149088235654, (47, 6609): 594.9533011711761, (47, 6610): 595.2738513950719, (47, 6611): 595.4004163587983, (47, 6614): 594.8269268995928, (47, 6615): 595.0393549414478, (47, 6616): 596.2031272787555, (47, 6617): 595.6994655904487, (47, 6618): 597.315226607016, (47, 6619): 594.0976533552748, (47, 6620): 596.2767727979976, (47, 6621): 595.4170843444888, (47, 6622): 595.5843797866514, (47, 6623): 594.780937375382, (47, 6624): 594.0541961905358, (47, 6625): 593.8650994707708, (47, 6626): 594.0306240706897, (47, 6627): 594.5772526743464, (47, 6628): 596.1519633474726, (47, 6629): 594.3577269394225, (47, 6630): 593.0449872392059, (47, 6632): 594.2400589388405, (47, 6634): 592.1307594666514, (47, 6635): 595.0754616916613, (47, 6636): 596.2696442446285, (47, 6637): 593.1671555737066, (47, 6638): 593.1925828300537, (47, 6639): 594.6907083084762, (47, 6640): 593.317021437025, (47, 6641): 595.4377351340704, (47, 6642): 593.2432310893523, (47, 6643): 593.9031467330105, (47, 6645): 594.2393414000733, (47, 6646): 596.9600487955585, (47, 6647): 593.4888363341829, (47, 6653): 594.9866533955358, (47, 6655): 594.6875371023946, (47, 6658): 592.0833208213403, (47, 6662): 593.227109060201, (47, 6819): 544.2735694538072, (47, 6996): 562.9301883875979, (47, 7059): 574.5283910538628, (47, 7187): 561.0324435444804, (47, 7304): 532.2695927425801, (47, 7528): 564.3154796451224, (47, 7720): 631.2401547293149, (47, 7793): 630.7083304840586, (47, 7807): 631.3571709716717, (47, 7808): 630.5809284028325, (47, 7831): 601.7185610825444, (47, 7850): 612.4687533130871, (47, 7852): 609.847714216704, (47, 8012): 626.8379338800845, (47, 8125): 643.1314756983197, (47, 8208): 652.6953427813405, (47, 8392): 611.7555031372498, (47, 8651): 488.46905468839793, (47, 9088): 539.2146579301378, (47, 9443): 471.12191362470696, (47, 9444): 472.96688792305747, (47, 9828): 428.5560647710417, (47, 9868): 419.81307255256513, (47, 10180): 644.7400646707347, (47, 10256): 674.8831041811369, (47, 10276): 660.1558881676305, (47, 10378): 661.3503940850694, (47, 10676): 639.2620912923794, (47, 10714): 621.089044430065, (47, 10730): 621.1278536594417, (47, 10862): 634.7304389886999, (47, 10881): 639.3871163106454, (47, 10883): 638.8134839668586, (47, 10885): 633.7436826983894, (47, 10891): 637.9284405707526, (47, 10909): 637.6560659274412, (47, 10911): 638.4500426607815, (47, 10913): 637.329790724978, (47, 10915): 637.3541451903255, (47, 10919): 638.0633252401427, (47, 11037): 605.165993598575, (47, 11039): 593.8910935376871, (47, 11516): 918.1360310199045, (47, 11856): 805.0125402050504, (47, 11857): 804.3774416637923, (47, 11861): 804.7453091535073, (47, 11881): 802.9385812154288, (47, 11902): 797.8718562342177, (47, 11911): 796.5159510706286, (47, 11914): 797.4117842805701, (47, 11922): 801.3288843887814, (47, 11924): 802.4104768368751, (47, 11926): 800.9251150911595, (47, 11950): 803.31865663614, (47, 11963): 808.156124656963, (47, 11983): 804.0716128748023, (47, 11985): 810.6243685973684, (47, 12009): 808.9711483842144, (47, 12010): 805.7200031725611, (47, 12018): 806.187381560397, (47, 12020): 807.221320001552, (47, 12021): 807.7095412942598, (47, 12024): 810.9828033613363, (47, 12025): 810.0231266992686, (47, 12027): 809.211813572228, (47, 12031): 805.1513029410456, (47, 12032): 806.4037682989947, (47, 12035): 808.5859907068157, (47, 12041): 811.4488762006945, (47, 12045): 765.2746916605469, (47, 12145): 785.45017076945, (47, 12275): 861.0106306941954, (47, 12294): 851.197561643961, (47, 12358): 877.2795874406721, (47, 12463): 886.7192883589233, (47, 12465): 886.3449436721506, (47, 12482): 891.861013863513, (47, 12503): 890.9937284912886, (47, 12506): 892.2721604440126, (47, 12549): 890.5607912594068, (47, 12559): 889.3752440909801, (47, 12569): 890.0491484103876, (47, 12572): 891.0321261270143, (47, 12574): 889.0944338535455, (47, 12576): 891.7993438320276, (47, 12591): 892.1715845640575, (47, 12608): 900.4001378986443, (47, 12696): 888.3142785785604, (47, 12710): 896.4004574232173, (47, 12728): 891.9955697659099, (47, 12766): 685.6692230119481, (47, 12771): 678.5469730145343, (47, 12790): 677.2450239780825, (47, 12795): 673.9970100446452, (47, 12797): 663.5490097905317, (47, 12798): 665.2312242614322, (47, 12811): 674.4180560200153, (47, 12830): 670.9464586715133, (47, 12848): 673.3443815588984, (47, 12850): 674.5988224348081, (47, 12852): 670.7455410364097, (47, 12854): 669.3280288953198, (47, 12859): 674.9634815486787, (47, 12861): 666.9770106968747, (47, 12865): 675.8114290574423, (47, 12866): 675.3136379680667, (47, 12867): 677.946269872734, (47, 12874): 676.6367138269062, (47, 12875): 677.8092108552407, (47, 12881): 673.142341962861, (47, 12883): 674.9236414459804, (47, 12885): 678.6881392917342, (47, 12888): 674.2629541426331, (47, 12889): 674.0180760641236, (47, 12892): 676.8522181096879, (47, 12893): 674.1685299135798, (47, 12896): 675.1756569864921, (47, 12906): 676.0317032499074, (47, 13018): 659.3361265254913, (47, 13071): 658.6683054053082, (47, 13131): 650.5093741169525, (47, 13146): 660.662262664459, (47, 13159): 643.3436260813404, (47, 13193): 648.9256977229787, (47, 13198): 633.7916064019272, (47, 13292): 653.2466327335999, (47, 13296): 660.2404620644678, (47, 13406): 621.1101946097441, (47, 13407): 620.3867194132831, (47, 13417): 617.7559986504622, (47, 13418): 619.3394045610294, (47, 13438): 627.7099672742858, (47, 13442): 629.619803603172, (47, 13443): 628.1542133971982, (47, 13764): 497.6457378774541, (47, 13766): 499.5012620785866, (47, 13771): 497.5165126431066, (47, 13783): 496.4182189022128, (47, 13784): 501.6042382481202, (47, 13792): 493.7058090101945, (47, 13824): 495.10400240045374, (47, 14017): 507.450998481544, (47, 14870): 637.5844446709291, (47, 14997): 553.1798569310705, (47, 15000): 553.8463190280171, (47, 15003): 555.5694627904163, (47, 15006): 556.201499416317, (47, 15007): 557.4967551643197, (47, 15056): 558.772719371142, (47, 15063): 557.9477315257482, (47, 15069): 558.0937705350293, (47, 15076): 558.0293348848592, (47, 15086): 553.5110858671193, (47, 15087): 552.8271654154789, (47, 15111): 548.6114509047808, (47, 15116): 551.0798189484176, (47, 15722): 517.6947831383652, (47, 15998): 509.3675713943047, (47, 16073): 252.94956369867097, (47, 16939): 124.89088089692032, (47, 16940): 126.33910261607616, (47, 16951): 121.33943151663179, (47, 16963): 122.02394218416015, (47, 16965): 121.74772088076357, (47, 16969): 120.05251170047086, (47, 16970): 122.57217369129847, (47, 16971): 122.96098694215468, (47, 16973): 121.79278692556342, (47, 16974): 120.47671002725171, (47, 16976): 123.3131914053296, (47, 16978): 124.00832815697207, (47, 16980): 124.22520254680356, (47, 16982): 119.20669687420715, (47, 17045): 24.0, (47, 17048): 24.0, (47, 17304): 844.9680375244467, (47, 17305): 843.0003795384308, (47, 17330): 844.3973984974864, (47, 17334): 842.7147814183644, (47, 17343): 846.0361687668907, (47, 17345): 841.8488791450756, (47, 17347): 843.7226498325717, (47, 17351): 839.4754222918867, (47, 17372): 842.1548947350545, (47, 17373): 846.0151090881897, (47, 17377): 846.222216958053, (47, 17382): 843.5439863681638, (47, 17383): 844.3029884960719, (47, 17389): 842.6589283182703, (47, 17400): 845.513598877862, (47, 17401): 845.5835729970937, (47, 17402): 845.5969793189306, (47, 17403): 845.8009440601021, (47, 17440): 841.163478366573, (47, 17455): 845.051056676779, (47, 17491): 844.7257813415529, (47, 17507): 842.8803319772519, (47, 17509): 844.5974256620226, (47, 17590): 837.5886932453049, (47, 17615): 834.0478920498417, (47, 17642): 835.1998237627761, (47, 17643): 834.7763056286573, (47, 17668): 834.167540540785, (47, 17721): 832.1835427348808, (47, 17754): 847.0888543687587, (47, 17769): 844.2548870008023, (47, 17776): 836.7769435355159, (47, 17804): 846.8764081701729, (47, 17809): 848.4163999480145, (47, 17824): 847.8930858540357, (47, 17837): 841.161910239838, (47, 17838): 840.8912093802434, (47, 17862): 839.5378988792908, (47, 17866): 843.0192281439574, (47, 17872): 838.7004135472877, (47, 17873): 835.9424825022918, (47, 17881): 840.108909378137, (47, 17947): 277.280700000891, (47, 17951): 278.33304421722187, (47, 17953): 279.39686895953827, (47, 17954): 279.8843168436332, (47, 17959): 276.003644723543, (47, 17963): 274.89703170929687, (47, 18000): 283.5395391122321, (47, 18001): 284.308900258073, (47, 18111): 311.36519111624966, (47, 18148): 346.1816877745077, (47, 18166): 335.2368053401868, (47, 18189): 317.1831368228209, (47, 18239): 847.0911003021046, (47, 18240): 846.9759667871575, (47, 18245): 847.1846790093122, (47, 18247): 846.7451892916171, (47, 18251): 847.0609707779126, (47, 18256): 847.2902448969888, (47, 18258): 846.848552269642, (47, 18259): 846.8656995089576, (47, 18260): 846.942212294342, (47, 18262): 847.1592352542679, (47, 18263): 847.3361091859223, (47, 18264): 847.4184460030634, (47, 18266): 847.186897989339, (47, 18267): 847.2810802785649, (47, 18268): 847.2909859807313, (47, 18269): 847.4682118565203, (47, 18275): 847.3841677720304, (47, 18285): 847.428773141338, (47, 18308): 845.5487899240733, (47, 18313): 844.6381970197098, (47, 18314): 844.7533114264554, (47, 18315): 847.7286104836661, (47, 18316): 847.5801671022609, (47, 18317): 847.6548563916893, (47, 18320): 847.9143065405392, (47, 18321): 847.8964431797343, (47, 18322): 848.0406884135258, (47, 18324): 848.3445641924028, (47, 18325): 848.9747379501952, (47, 18326): 848.7459619631499, (47, 18327): 847.6139305278062, (47, 18329): 849.4035562025314, (47, 18330): 848.6821779108677, (47, 18331): 848.3247543388377, (47, 18332): 847.8891128974756, (47, 18333): 848.7327237367052, (47, 18336): 848.5743262381998, (47, 18337): 848.8716864859256, (47, 18403): 847.8180963837443, (47, 18432): 835.3986899260295, (47, 18451): 843.7992995664564, (47, 18466): 852.3148658329864, (47, 18481): 848.2368248516344, (47, 18483): 848.1452638996351, (47, 18484): 847.8684048231856, (47, 18485): 847.1264770120694, (47, 18486): 848.3797642011152, (47, 18487): 847.6818990998632, (47, 18489): 847.9761513683887, (47, 18490): 849.027369922848, (47, 18491): 849.4075551834295, (47, 18492): 846.7939986297532, (47, 18493): 848.3522680440575, (47, 18494): 847.748316468587, (47, 18495): 848.7576220723138, (47, 18496): 848.2849656749232, (47, 18497): 847.6043963563853, (47, 18498): 847.4229054064295, (47, 18499): 847.9809897692419, (47, 18501): 847.7364986688592, (47, 18502): 847.3896692816303, (47, 18503): 847.0138304315477, (47, 18504): 848.3308006162619, (47, 18506): 848.0485299248595, (47, 18507): 847.7686878700971, (47, 18508): 847.990842517568, (47, 18509): 848.0835252805683, (47, 18510): 847.1487953952212, (47, 18511): 848.6436404432553, (47, 18512): 848.0501394078076, (47, 18515): 848.4929692313846, (47, 18516): 848.8172645055606, (47, 18517): 848.5075642040562, (47, 18518): 849.0340709019368, (47, 18519): 848.3561235335977, (47, 18520): 847.777212019292, (47, 18522): 849.7075822291185, (47, 18523): 849.8861942246381, (47, 18532): 850.5346293439271, (47, 18535): 849.2886568370361, (47, 18537): 848.5949891862514, (47, 18539): 848.7913819621745, (47, 18540): 848.9263743883008, (47, 18541): 849.3126242132247, (47, 18542): 849.5485053567204, (47, 18543): 848.4168241792108, (47, 18546): 849.1207860620622, (47, 18555): 850.2172352161364, (47, 18556): 850.4832831578648, (47, 18565): 850.5858138844916, (47, 18567): 851.0977768058711, (47, 18568): 850.4180410965159, (47, 18577): 854.6648877940537, (47, 18583): 853.6841360198054, (47, 18605): 854.2543830094195, (47, 18608): 851.8521043212957, (47, 18616): 858.239812986587, (47, 18618): 861.8016889824773, (47, 18625): 859.9310235790233, (47, 18645): 856.644498234087, (47, 18646): 857.6605807850198, (47, 18653): 855.5153210988143, (47, 18654): 858.2693170355105, (47, 18655): 856.6049404131799, (47, 18666): 866.4176120571414, (47, 18837): 843.5820439861602, (47, 18974): 841.4530815448292, (47, 18999): 843.069315149039, (47, 19000): 844.0638001085318, (47, 19174): 790.6613762837569, (47, 19342): 808.9428778347719, (47, 19455): 802.4766976867396, (47, 19555): 751.0249203500392, (47, 19564): 751.9296189454082, (47, 19573): 750.2548234551124, (47, 19586): 749.6380143891322, (47, 19605): 750.7467436506148, (47, 19611): 751.9555405067207, (47, 19614): 751.9528696759504, (47, 19641): 774.6378834479611, (47, 19702): 773.6121504445018, (47, 19713): 772.0804269241479, (47, 19731): 745.9170202496972, (47, 19819): 793.6766075109841, (47, 19893): 762.2409448344886, (47, 19899): 773.7219163567141, (47, 19929): 765.1685402182381, (47, 19951): 787.7140957226505, (47, 19962): 767.1785515030239, (47, 19970): 771.7961764545897, (47, 19971): 771.979485200705, (47, 19972): 770.1361222350233, (47, 19975): 769.1861001361023, (47, 19978): 792.2027003747171, (47, 19987): 792.5508534271278, (47, 19989): 786.3382206155383, (47, 20039): 793.6743836890162, (47, 20043): 796.2173813013078, (47, 20047): 794.1822404125475, (47, 20052): 787.3508674553203, (47, 20054): 787.9188442593285, (47, 20085): 818.7550136305122, (47, 20104): 820.6928347597933, (47, 20132): 808.875888006471, (47, 20203): 761.6294926261712, (47, 20280): 759.2375569936243, (47, 20285): 758.6512863598624, (47, 20290): 760.2952438357469, (47, 20297): 758.1807362376671, (47, 20309): 794.1546306060729, (47, 20453): 826.1259024839482, (47, 20485): 744.884191469849, (47, 20520): 739.5100031948082, (47, 20526): 737.669048176254, (47, 20698): 445.0900502487562, (47, 20868): 381.8085116983255, (47, 21042): 684.0937032356147, (47, 21057): 696.5955233553465, (47, 21066): 690.8896284155006, (47, 21075): 687.9271625925215, (47, 21093): 685.6273253038117, (47, 21098): 695.3703255125631, (47, 21127): 685.4378673619016, (47, 21130): 688.0883481247297, (47, 21144): 687.1751205472268, (47, 21146): 684.6173108596641, (47, 21147): 686.7988087958967, (47, 21148): 689.1685105519632, (47, 21153): 681.8114568733312, (47, 21293): 705.602248201335, (47, 21426): 697.0855773735267, (47, 21442): 709.4653025768532, (47, 21451): 710.6843425310709, (47, 21466): 703.5229688116857, (47, 21469): 705.6190823259407, (47, 21471): 702.4483353498424, (47, 21473): 704.2461088697587, (47, 21475): 702.7099053355286, (47, 21482): 706.7263522777926, (47, 21484): 706.4042073343098, (47, 21488): 705.1161084750366, (47, 21494): 702.9985190698087, (47, 21498): 704.4836281330537, (47, 21500): 702.3713077337409, (47, 21514): 707.5695467220935, (47, 21537): 702.6095172810847, (47, 21662): 710.1735388254687, (47, 21691): 702.2153401991345, (47, 21757): 685.7704459134313, (47, 21777): 661.7650400483237, (47, 21778): 659.7667176897643, (47, 21779): 661.1568209439829, (47, 21790): 663.7195040454449, (47, 21802): 664.148526495948, (47, 21824): 666.4961708251806, (47, 21874): 662.0113605092569, (47, 21879): 661.3371746424592, (47, 21983): 667.0090355977956, (47, 22002): 690.394420921688, (47, 22132): 670.5508890504635, (47, 22261): 438.0567836058984, (47, 22298): 443.81429950913054, (47, 22339): 432.2069169931492, (47, 22508): 469.9436912356551, (47, 22841): 156.3227552546982, (47, 22842): 155.3137772981248, (47, 22874): 150.47462500362792, (47, 22941): 154.0697815432961, (47, 22956): 154.01322524166315, (47, 22960): 156.69503760347436, (47, 22968): 143.77835962084336, (47, 22970): 146.02207548362466, (47, 22974): 137.87641496616547, (47, 22980): 139.0499511728315, (47, 23025): 126.65815356609227, (47, 23028): 123.84463672471054, (47, 23081): 111.39293880839234, (47, 23104): 88.49765607386088, (47, 23147): 114.92273498400752, (47, 23298): 743.9218082829644, (47, 23376): 738.2961302860945, (47, 23381): 736.2647351468564, (47, 23529): 748.6045690759669, (47, 23556): 745.1799919345735, (47, 23718): 739.3529406279237, (47, 24001): 776.973022510245, (47, 24094): 789.7086676526927, (47, 24129): 795.3070410811741, (47, 24174): 784.6130089032017, (47, 24235): 797.6727678490251, (47, 24259): 802.4071818215309, (47, 24260): 802.1002766935196, (47, 24261): 800.8091229326169, (47, 24305): 808.5401086514363, (47, 24306): 809.7496811506411, (47, 24307): 808.043652116803, (47, 24308): 789.3012453733053, (47, 24498): 820.7627388964289, (47, 24499): 820.9320360608923, (47, 24500): 819.8456096971148, (47, 24668): 810.3019608307985, (47, 24711): 828.8798576057507, (47, 24756): 833.6073235231328, (47, 24788): 834.8086135433033, (47, 24809): 829.5438031243332, (47, 24813): 831.1003149523661, (47, 24821): 830.5486067808182, (47, 24825): 831.1323936918619, (47, 24832): 829.0473448433822, (47, 24833): 829.9514173766461, (47, 24835): 830.9051719021439, (47, 24837): 832.218495939314, (47, 24840): 828.9717859335054, (47, 24841): 830.2352108975916, (47, 24844): 829.1002830277804, (47, 24845): 829.5824274721797, (47, 24846): 829.9846675919446, (47, 24849): 830.5193721709519, (47, 24850): 831.4831662748992, (47, 24863): 818.2797347982896, (47, 24866): 819.8626451868361, (47, 24885): 822.0694126979464, (47, 24886): 822.3995242211221, (47, 24889): 825.2487360764646, (47, 24903): 826.312027255523, (47, 24909): 819.9653786653913, (47, 24999): 887.0800835098959, (47, 25019): 884.4239460185039, (47, 25028): 886.3198734336818, (47, 25137): 764.2579602502524, (47, 25145): 766.4792542075603, (47, 25208): 792.8124845379901, (47, 25233): 789.8189396700606, (47, 25371): 763.8184842919036, (47, 25377): 757.2879008905389, (47, 25828): 642.7978929825558, (47, 25851): 624.57550432696, (47, 25874): 641.3351954441852, (47, 25898): 649.6442814378901, (47, 25946): 640.9719157822535, (47, 26047): 678.8788013509022, (47, 26066): 715.9325097207744, (47, 26197): 691.4037257125847, (47, 26212): 590.987290147113, (47, 26253): 585.8924278388722, (47, 26254): 587.642145844986, (47, 26257): 590.0345040775861, (47, 26258): 587.0927691973393, (47, 26260): 588.5593357323751, (47, 26266): 585.2151026753443, (47, 26267): 587.1714711216192, (47, 26271): 587.4036366084814, (47, 26304): 604.9360445810867, (47, 26305): 604.350351428817, (47, 26363): 638.3174526533542, (47, 26441): 477.853715681652, (47, 26442): 477.45773951811685, (47, 26450): 479.6568627262807, (47, 26459): 483.194525584679, (47, 26462): 484.3903127880445, (47, 26467): 478.68085980596203, (47, 26471): 478.5350483473218, (47, 26472): 478.1986379635764, (47, 26473): 477.7756277756926, (47, 26476): 473.6983950632866, (47, 26485): 480.5241119608469, (47, 26493): 478.72498410481717, (47, 26524): 485.04579871080455, (47, 26525): 484.33923798774896, (47, 26556): 479.4757902755178, (47, 26560): 482.5246317665441, (47, 26561): 484.4181707807577, (47, 26564): 479.2285863723194, (47, 26569): 483.7768630320531, (47, 26570): 483.1850811099124, (47, 26573): 481.35134928703815, (47, 26581): 480.05038259544244, (47, 26583): 481.3180246528012, (47, 26593): 478.33608927438945, (47, 26837): 476.90121400735285, (47, 26844): 476.25164400698645, (47, 26863): 474.3595368398236, (47, 26893): 471.0440044901884, (47, 26902): 470.0319897031046, (47, 26905): 474.0643320768403, (47, 26912): 472.3282540301134, (47, 26921): 472.9702956482069, (47, 26922): 470.4240983183693, (47, 27212): 543.5252504580892, (47, 27218): 547.3725125672796, (47, 27239): 541.7859868740862, (47, 27257): 541.2128542256759, (47, 27274): 540.9349306439616, (47, 27279): 539.8070794737587, (47, 27282): 540.5102122538507, (47, 27283): 542.6353211862468, (47, 27285): 539.8785434877154, (47, 27286): 538.3537421449857, (47, 27290): 540.9162213725093, (47, 27295): 543.1921704003632, (47, 27300): 541.3062735425923, (47, 27344): 537.6370784107411, (47, 27366): 535.6051455888149, (47, 27383): 537.2132162555778, (47, 27398): 539.4128760485694, (47, 27406): 540.9965730213529, (47, 27407): 541.7943110567879, (47, 27426): 551.094102930889, (47, 27432): 551.4331982190747, (47, 27460): 552.3287299667367, (47, 27523): 516.1965428341307, (47, 27545): 526.580460058306, (47, 27602): 505.68789499042293, (47, 27606): 507.1816237189732, (47, 27646): 496.6032449708909, (47, 27667): 492.3460805418499, (47, 27672): 493.1153503657862, (47, 27674): 493.2136711159673, (47, 27688): 496.51308342743556, (47, 27692): 491.2649465997211, (47, 27693): 491.68131610949547, (47, 27705): 490.5906606018182, (47, 27712): 489.43422101249956, (47, 27786): 547.161714202915, (47, 27790): 562.4048985638924, (47, 27791): 564.5413533007575, (47, 27795): 546.4085220010531, (47, 27801): 556.4700832542959, (47, 27813): 545.2499892900006, (47, 27816): 548.4307548979046, (47, 27823): 556.9781718555549, (47, 27830): 552.1071767893591, (47, 27884): 493.1058287613617, (47, 27885): 496.7244560217599, (47, 27896): 495.02677288608425, (47, 27919): 495.9481536433675, (47, 27922): 494.8470754340149, (47, 27930): 494.9420212654903, (47, 27934): 494.14616664670297, (47, 27935): 493.1825381843296, (47, 27948): 453.60051825193256, (47, 27951): 470.19920198335365, (47, 28061): 363.4924053686377, (47, 28290): 328.37975470585343, (47, 28292): 322.9845827905219, (47, 28293): 326.94519621925093, (47, 28295): 324.1440148326005, (47, 28296): 326.7755071410117, (47, 28297): 330.9057883929781, (47, 28302): 328.3606380799946, (47, 28310): 151.425416601541, (47, 28313): 150.1022542522573, (47, 28372): 149.06247752155178, (47, 28398): 148.8811570928339, (47, 28399): 149.67702970338138, (47, 28400): 148.41664506531762, (47, 28401): 151.70871958308808, (47, 28445): 151.71331770490866, (47, 28475): 154.54729214377153, (47, 28885): 799.6522831257662, (47, 28886): 798.6369340375545, (47, 28915): 799.8006028349595, (47, 28916): 798.8162073130178, (47, 28917): 798.2841386142263, (47, 28921): 801.6001458656268, (47, 28931): 801.3728060782394, (47, 28945): 796.8279107499105, (47, 28982): 797.8768430713345, (47, 29219): 805.1748871140995, (47, 29228): 800.2824955932107, (47, 29246): 832.516893826852, (47, 29248): 832.2577316375459, (47, 29282): 825.6079920996528, (47, 29290): 835.5626040015325, (47, 29291): 834.2904002229734, (47, 29292): 835.5090069850015, (47, 29293): 832.9178053771651, (47, 29294): 835.0590238799552, (47, 29298): 833.1639157236212, (47, 29299): 832.9925432300339, (47, 29304): 830.4597265245993, (47, 29317): 824.1723091333873, (47, 29323): 823.6780386276463, (47, 29330): 826.716723237654, (47, 29331): 828.1823163161147, (47, 29344): 806.1355443454163, (47, 29445): 750.9395539879629, (47, 29724): 195.3240794126983, (47, 29738): 195.43298355472623, (47, 29745): 196.67787438957575, (47, 29748): 204.5893590345729, (47, 29750): 208.06165093675074, (47, 29759): 203.4924196927753, (47, 29772): 203.99820267800317, (47, 29781): 204.10821996891443, (47, 29784): 200.6526853845291, (47, 29790): 205.60395791035944, (47, 29811): 208.78801779061357, (47, 29817): 230.16436459339758, (47, 29818): 230.3915586485115, (47, 29929): 191.7399062820672, (47, 30039): 171.7255749657595, (47, 30066): 157.8282396918574, (47, 30116): 173.2467288667379, (47, 30238): 203.98346818045036, (47, 30248): 165.7273066614879, (47, 30260): 163.4261844337655, (47, 30545): 781.9860070023641, (47, 30733): 728.8128034787462, (47, 30756): 717.4413349419591, (47, 30921): 741.7594141446632, (47, 31079): 591.2544519297802, (47, 31149): 588.340786773208, (47, 31154): 587.8336175614347, (47, 31160): 588.0430610716566, (47, 31163): 587.0569684060087, (47, 31189): 568.0538278830262, (47, 31215): 568.5560062566044, (47, 31259): 563.0868743335034, (47, 31262): 561.1993792326067, (47, 31430): 591.4497237380081, (47, 31568): 529.6147345510294, (47, 31751): 578.8298038202792, (50, 109): 518.47662585044, (50, 872): 178.0816846049088, (50, 873): 178.44281761141707, (50, 877): 177.17748209881913, (50, 879): 177.1231650636058, (50, 884): 174.23862505030039, (50, 889): 174.99994614066335, (50, 891): 174.42698814514526, (50, 892): 177.65582619434417, (50, 894): 178.0652378060698, (50, 896): 179.57369532239133, (50, 903): 175.90660058644548, (50, 909): 179.0304557523556, (50, 910): 180.20812807348216, (50, 912): 179.75609837811393, (50, 913): 178.88465817556093, (50, 916): 180.06562226478513, (50, 926): 181.69620662876596, (50, 927): 181.82357612396873, (50, 948): 174.48831047670856, (50, 961): 179.22620827119837, (50, 962): 179.99671918974767, (50, 963): 180.62668935220805, (50, 967): 176.52460110521466, (50, 974): 173.69632784175914, (50, 998): 175.75906846558811, (50, 1014): 204.0540250244011, (50, 1086): 208.2355691386214, (50, 1087): 212.03200931932855, (50, 1089): 209.80682056035806, (50, 1090): 209.59055124194677, (50, 1092): 209.95288518443087, (50, 1097): 208.91619568963407, (50, 1107): 212.5685744692854, (50, 1387): 400.1718306047329, (50, 1554): 422.9985059755757, (50, 1827): 206.4352357839559, (50, 1828): 206.95340874468698, (50, 1829): 206.97671074284972, (50, 1830): 205.1207455488683, (50, 1831): 205.55344896470282, (50, 1832): 205.52601853668082, (50, 1833): 205.81899408547665, (50, 1836): 205.93426441884358, (50, 1841): 206.60715275264855, (50, 1843): 206.15600074620724, (50, 1844): 206.08758707702296, (50, 1845): 205.31347596063767, (50, 1847): 204.39099185798466, (50, 1848): 204.88245458638173, (50, 1849): 206.95939709252727, (50, 1850): 207.45635947078827, (50, 1851): 204.5343417905435, (50, 1852): 203.9471868501117, (50, 1854): 204.68146299148813, (50, 1856): 203.47990881133967, (50, 1857): 204.5027528521256, (50, 1858): 207.1585773459486, (50, 1861): 206.40037370240626, (50, 1866): 202.90154640200413, (50, 1867): 207.16714278054724, (50, 1868): 207.32217563522153, (50, 1870): 205.23532787799812, (50, 1871): 207.615887439104, (50, 1875): 205.07856503317308, (50, 1880): 204.36652630398015, (50, 1882): 203.61766631992558, (50, 1883): 208.1831701570682, (50, 1889): 205.70494022044906, (50, 1893): 208.04620768538499, (50, 1894): 207.8298619827108, (50, 1899): 205.79305684525082, (50, 1900): 206.3048605264673, (50, 1902): 208.74132753793762, (50, 1905): 208.84674138303183, (50, 1907): 205.90530329388594, (50, 1910): 206.8833092097386, (50, 1917): 212.01073735762682, (50, 1920): 206.50572191303382, (50, 1935): 210.13689012031747, (50, 1937): 210.37061183883753, (50, 1946): 206.38220639389087, (50, 1949): 207.21850254956482, (50, 1950): 203.8015525140811, (50, 1951): 205.09081695672018, (50, 1952): 204.0724625561792, (50, 1953): 205.89101675409944, (50, 1954): 204.35487479063218, (50, 1958): 206.37095371346336, (50, 1960): 206.82447523486618, (50, 1968): 207.0102126966672, (50, 1969): 211.48092811552246, (50, 1974): 210.19913605072776, (50, 1975): 209.7754861380898, (50, 1979): 209.29902082735165, (50, 1980): 207.9438224721233, (50, 1981): 209.11091076167827, (50, 1985): 209.77277617605228, (50, 1994): 200.19913292034983, (50, 2011): 203.1795187043729, (50, 2019): 206.13566208142464, (50, 2020): 205.72314068740852, (50, 2029): 203.03488105309893, (50, 2030): 205.4577943992693, (50, 2032): 202.00318120211102, (50, 2033): 204.00834567050407, (50, 2034): 203.40780978064092, (50, 2036): 198.53297449070683, (50, 2037): 199.87047287219062, (50, 2038): 202.79854180684396, (50, 2042): 209.39879210018267, (50, 2050): 204.56159810836945, (50, 2051): 203.83864890771565, (50, 2053): 204.28712516150173, (50, 2054): 204.84236019681026, (50, 2066): 203.60389280958182, (50, 2067): 203.9309894527655, (50, 2071): 199.48511422889226, (50, 2072): 201.04079185488985, (50, 2073): 199.87562726084164, (50, 2074): 199.300944225085, (50, 2080): 196.44743504440015, (50, 2082): 201.73280827684292, (50, 2083): 202.57887821649527, (50, 2089): 201.84204167735285, (50, 2090): 202.74218164591483, (50, 2092): 202.3906356553617, (50, 2098): 198.00273986545116, (50, 2099): 198.22362285920653, (50, 2101): 197.29385195174976, (50, 2102): 201.02493651461205, (50, 2103): 199.608288627031, (50, 2104): 198.55506933326413, (50, 2106): 202.71503010689034, (50, 2112): 197.23411458106312, (50, 2113): 201.19667204779267, (50, 2114): 201.09347705765336, (50, 2117): 202.7771505854245, (50, 2123): 222.4659222741261, (50, 2124): 223.18855333553424, (50, 2134): 219.3521535307395, (50, 2138): 222.19142228518487, (50, 2141): 220.14881715887125, (50, 2148): 214.4457858575606, (50, 2150): 218.06527722598977, (50, 2151): 218.3168156529177, (50, 2152): 217.19699966677692, (50, 2153): 215.32914218064775, (50, 2154): 212.71327695849908, (50, 2155): 211.22793049611604, (50, 2156): 211.47994744932026, (50, 2157): 208.13590309384622, (50, 2160): 219.93810424453392, (50, 2161): 216.3881464024628, (50, 2162): 212.94741664245723, (50, 2163): 212.1291953290572, (50, 2164): 211.65867387875454, (50, 2168): 214.8392207762189, (50, 2172): 212.42942075524098, (50, 2174): 217.36486838971658, (50, 2178): 212.13618282189793, (50, 2179): 211.4086900365092, (50, 2183): 221.34986730314594, (50, 2185): 220.97377724527703, (50, 2186): 220.61767151195104, (50, 2190): 220.81865917865915, (50, 2192): 220.0228873925781, (50, 2193): 221.7897139410643, (50, 2194): 220.9860183810682, (50, 2195): 219.9614589452987, (50, 2197): 219.75815347769816, (50, 2205): 217.35085003430325, (50, 2207): 214.50314361858418, (50, 2208): 215.91682619944257, (50, 2212): 224.01823526668588, (50, 2214): 191.7175234598235, (50, 2225): 191.21159141200093, (50, 2231): 207.60654843593687, (50, 2278): 194.6585756845483, (50, 2284): 195.25867054043235, (50, 2285): 194.4409257242301, (50, 2291): 186.9315834719232, (50, 2292): 191.74468528685335, (50, 2307): 193.8774380741851, (50, 2313): 185.12245650908528, (50, 2317): 192.1562518024621, (50, 2319): 191.9696024133176, (50, 2321): 192.1311773010857, (50, 2323): 193.2537491464342, (50, 2326): 198.94501925757672, (50, 2327): 198.11450120398314, (50, 2329): 197.42053973053066, (50, 2330): 196.33562504581118, (50, 2332): 197.11927417883416, (50, 2344): 196.81480544260876, (50, 2346): 195.8942060126926, (50, 2361): 203.10908633169666, (50, 2368): 208.3754312167276, (50, 2374): 208.65123141757383, (50, 2375): 209.38669583998293, (50, 2377): 206.80436547053057, (50, 2378): 209.61078909051318, (50, 2379): 208.84735159617068, (50, 2380): 209.7662073046347, (50, 2383): 208.17804747616034, (50, 2385): 208.96995460338374, (50, 2395): 209.79714496003763, (50, 2397): 208.08187426523264, (50, 2398): 205.90066867308505, (50, 2399): 207.42169626499575, (50, 2400): 207.18923042662507, (50, 2402): 206.56948139540285, (50, 2403): 207.21836099830384, (50, 2404): 207.73341503506825, (50, 2405): 205.86086470672467, (50, 2407): 207.8912744903692, (50, 2408): 208.2922523675237, (50, 2409): 206.56109374251625, (50, 2411): 205.81071792156737, (50, 2412): 206.16342079833217, (50, 2413): 206.50925108201014, (50, 2414): 205.4442111337251, (50, 2422): 205.12379714018957, (50, 2424): 206.65601747335995, (50, 2426): 207.08371004297837, (50, 2433): 205.30578120678328, (50, 2436): 204.05590628620925, (50, 2437): 200.5103539371582, (50, 2440): 201.53803022097182, (50, 2445): 212.56628932187547, (50, 2447): 210.87491476697883, (50, 2454): 213.13229801733638, (50, 2455): 213.84028726610362, (50, 2460): 206.11290654693556, (50, 2461): 206.9269935306465, (50, 2471): 218.11465009221658, (50, 2492): 183.21752298045305, (50, 2511): 178.0015608581002, (50, 2523): 180.51730629876172, (50, 2525): 178.37840310163668, (50, 2535): 190.3088300403027, (50, 2537): 188.28746807351138, (50, 2538): 190.21010771064013, (50, 2539): 187.1429665609138, (50, 2540): 191.16092324939163, (50, 2542): 191.73480866207822, (50, 2559): 222.31661831596048, (50, 2575): 217.1399710499743, (50, 2599): 187.67402046616365, (50, 2600): 193.50912348834757, (50, 2607): 192.473548618378, (50, 2627): 175.80499970549758, (50, 2647): 179.6772561958738, (50, 2674): 178.95132780762273, (50, 2681): 177.32475207267214, (50, 2683): 180.18384352590098, (50, 2686): 177.83790528651016, (50, 2689): 210.24325049707147, (50, 2690): 210.23511005686802, (50, 2713): 212.82602743922936, (50, 2714): 213.02211204660216, (50, 2715): 213.90829153584022, (50, 2739): 213.2348988780532, (50, 2740): 208.8890143059029, (50, 2741): 209.42448919190966, (50, 2749): 211.62185295616402, (50, 2750): 212.0260564140539, (50, 2752): 212.7169643110242, (50, 2755): 213.3358131510583, (50, 2758): 213.02532478873638, (50, 2759): 213.08465612502883, (50, 2769): 212.20274614816194, (50, 2771): 209.96279061231675, (50, 2779): 209.15497006673868, (50, 2784): 198.7990867444408, (50, 2800): 199.8051148143035, (50, 2802): 206.54025214722307, (50, 2803): 206.35217956742738, (50, 2804): 205.82449180210202, (50, 2805): 206.8633267420149, (50, 2807): 206.94462086059687, (50, 2809): 206.31751455113798, (50, 2812): 201.01568409362542, (50, 2814): 205.24115129430055, (50, 2817): 204.64780942309346, (50, 2819): 207.40850033113148, (50, 2823): 200.46879732916307, (50, 2832): 207.77231349090795, (50, 2836): 203.8223887960544, (50, 2839): 207.07397386576022, (50, 2841): 205.20689382024844, (50, 2843): 205.05708201922263, (50, 2846): 204.1043063826191, (50, 2849): 208.17880375550803, (50, 2852): 207.35899228723358, (50, 2853): 208.5496429372919, (50, 2876): 208.43387528587377, (50, 2877): 211.55456698301305, (50, 2885): 211.7670720546685, (50, 2918): 208.86696753533275, (50, 2921): 210.0170411859017, (50, 2925): 205.33215942610585, (50, 2926): 204.26642000734108, (50, 2930): 205.95972839370185, (50, 2931): 205.3668037808143, (50, 2938): 208.59503545496216, (50, 2940): 213.93803302332805, (50, 2947): 209.8013246655707, (50, 2949): 206.57256672427005, (50, 2950): 206.88751604765403, (50, 2952): 206.21465325789327, (50, 2958): 206.20349429671646, (50, 2959): 207.18464422613718, (50, 2960): 208.54618404922056, (50, 2961): 207.70272827395556, (50, 2963): 205.4745384683385, (50, 2968): 205.7307368572819, (50, 2976): 205.47260715225926, (50, 2981): 190.86896560230568, (50, 2982): 190.2313267227168, (50, 2984): 189.50399756239526, (50, 3003): 188.05401928260972, (50, 3046): 183.33244218804757, (50, 3050): 187.94193995087414, (50, 3051): 188.59649563312072, (50, 3053): 186.99221651365627, (50, 3069): 194.6364022877417, (50, 3071): 187.47181250627293, (50, 3080): 211.59923995222488, (50, 3199): 184.70058310097212, (50, 3200): 183.03436766759978, (50, 3205): 192.82661968749872, (50, 3209): 183.84403646504072, (50, 3215): 183.20447211026678, (50, 3217): 181.24330542040065, (50, 3249): 183.46478631236505, (50, 3263): 198.31722659583406, (50, 3289): 188.39482322415168, (50, 3301): 188.63430044307094, (50, 3302): 188.00858352203159, (50, 3307): 187.1517211610315, (50, 3310): 189.47864315924645, (50, 3391): 193.30860841788254, (50, 3509): 133.51936993583752, (50, 3510): 134.83884584062665, (50, 3511): 134.34827774809295, (50, 3512): 135.50783599942358, (50, 3514): 135.55184320712812, (50, 3519): 128.62073229528892, (50, 3536): 131.90084672562045, (50, 3545): 130.27570230186794, (50, 3548): 132.82823696570438, (50, 3572): 130.66566113335327, (50, 3581): 130.99558574682675, (50, 3583): 133.46135468600693, (50, 3601): 125.58294477312104, (50, 3656): 126.56665272426584, (50, 3669): 127.21529135896189, (50, 3670): 125.91110644133242, (50, 3695): 133.67780856769554, (50, 3696): 132.73833446913528, (50, 3782): 141.21508837632757, (50, 3792): 141.04204136109013, (50, 3989): 710.6301093247142, (50, 4008): 717.4259152953516, (50, 4031): 715.7134033189329, (50, 4045): 714.5123473510096, (50, 4144): 716.0658120713566, (50, 4145): 710.5144784007563, (50, 4164): 713.7410067765038, (50, 4168): 712.2160965884135, (50, 4173): 712.0794183525495, (50, 4181): 707.9282754166793, (50, 4228): 702.6623900090207, (50, 4248): 702.7750943436832, (50, 4254): 670.9076121799617, (50, 4260): 670.4990886262991, (50, 4262): 673.2503569798904, (50, 4273): 672.3782000137976, (50, 4319): 652.4254642089114, (50, 4326): 651.5627129323327, (50, 4328): 651.7204482762525, (50, 4334): 653.5210744068241, (50, 4335): 653.0696129715535, (50, 4372): 649.1980306406039, (50, 4413): 672.1417586426245, (50, 4434): 648.304907774311, (50, 4447): 651.6022533987156, (50, 4452): 648.5910457092818, (50, 4463): 599.2996684545406, (50, 4465): 601.0233306453695, (50, 4619): 673.8823773383514, (50, 4645): 679.2511585280674, (50, 4657): 678.2937402595934, (50, 4666): 676.1467791363982, (50, 4676): 679.7891248116314, (50, 4678): 680.6676320756127, (50, 4689): 678.0192805759643, (50, 4704): 696.0734190404199, (50, 4726): 735.8995835729339, (50, 4727): 735.1488267504386, (50, 4730): 733.7091155620996, (50, 4731): 734.0143820845103, (50, 4734): 735.4504295974413, (50, 4735): 734.6466117113033, (50, 4736): 734.9252162115577, (50, 4737): 733.5534092947224, (50, 4738): 733.6569442088729, (50, 4756): 734.358359637852, (50, 4760): 731.0451018018128, (50, 4761): 731.652905822937, (50, 4762): 729.9071009920368, (50, 4765): 731.3601997955283, (50, 4773): 737.4686234944731, (50, 4774): 736.6278305777539, (50, 4790): 736.9952696383071, (50, 4795): 736.3821532048713, (50, 4799): 736.8618952534115, (50, 4801): 738.2001556769916, (50, 4804): 736.8507707616077, (50, 4805): 736.3443947288366, (50, 4806): 736.0904494263974, (50, 4815): 735.220159157125, (50, 4816): 737.1791331818529, (50, 4817): 737.3536080052145, (50, 4826): 736.29418819877, (50, 4830): 735.1431066461965, (50, 4839): 733.2229086277931, (50, 4840): 733.8099969392296, (50, 4841): 732.1603377742783, (50, 4846): 731.6725864250029, (50, 4848): 731.3349246255322, (50, 4850): 731.9887210277817, (50, 4871): 724.040135492425, (50, 4883): 730.4416371878325, (50, 4900): 727.3821965825477, (50, 4901): 726.3161116310465, (50, 4917): 670.320773094317, (50, 4931): 664.6325617756277, (50, 4944): 671.0959533274652, (50, 4956): 665.5453456008343, (50, 4958): 665.1227979215154, (50, 4959): 663.8660142243008, (50, 4961): 666.8025252465073, (50, 4966): 664.005616601352, (50, 5207): 657.6758989025012, (50, 5272): 557.0071799892944, (50, 5283): 559.0023359181422, (50, 5287): 561.6183504089146, (50, 5289): 562.4725286235413, (50, 5293): 557.9308565112221, (50, 5295): 563.5951608067936, (50, 5296): 563.2072543961773, (50, 5298): 562.94642395073, (50, 5303): 564.3226854901507, (50, 5305): 555.1638468104508, (50, 5306): 553.1014431293975, (50, 5307): 554.0859462539581, (50, 5308): 555.980100538109, (50, 5313): 556.3315593156311, (50, 5314): 557.7369863192908, (50, 5317): 555.766901953148, (50, 5319): 562.2885289426084, (50, 5324): 561.411070523212, (50, 5326): 560.8672005231247, (50, 5348): 552.3347427266658, (50, 5351): 553.3467695950404, (50, 5399): 563.1117694605763, (50, 5413): 555.1647273894262, (50, 5422): 564.5493745583242, (50, 5445): 559.7661183291516, (50, 5448): 557.8316676849986, (50, 5456): 557.010834737605, (50, 5467): 558.7116629192011, (50, 5624): 538.6503759789872, (50, 5671): 606.156668483733, (50, 5672): 603.5447190720874, (50, 5797): 637.5722865734298, (50, 5871): 587.2062398628226, (50, 5976): 564.127081377457, (50, 6118): 63.544458086235174, (50, 6248): 107.24568879605545, (50, 6345): 438.21859142965144, (50, 6352): 431.66950900650744, (50, 6354): 439.82214341615173, (50, 6359): 441.11553175535494, (50, 6376): 432.7337397712967, (50, 6378): 439.04430536200243, (50, 6381): 440.5804935416596, (50, 6383): 436.82812063192733, (50, 6396): 439.8852614211332, (50, 6399): 438.3050754026179, (50, 6408): 431.90118878145336, (50, 6409): 435.00030384238283, (50, 6419): 424.4484958091382, (50, 6422): 432.76661293053627, (50, 6423): 432.23788403678685, (50, 6424): 439.20900892065885, (50, 6439): 437.9633595239012, (50, 6464): 436.15860564722175, (50, 6465): 435.4834498826187, (50, 6469): 436.27674277123396, (50, 6470): 435.870774704564, (50, 6472): 443.3366931330924, (50, 6480): 442.0290433217221, (50, 6486): 446.12916150166814, (50, 6497): 444.74827357582825, (50, 6503): 436.8127975780289, (50, 6508): 437.13979534418655, (50, 6509): 438.4779741902897, (50, 6521): 442.912567633768, (50, 6544): 442.58462342761817, (50, 6552): 434.01114371139073, (50, 6553): 432.99741063709064, (50, 6554): 431.9645045470833, (50, 6578): 435.6897534006594, (50, 6582): 435.0650986584962, (50, 6601): 436.1785650320897, (50, 6609): 444.2533399664806, (50, 6610): 444.56412805689945, (50, 6611): 444.7155618253809, (50, 6614): 444.1591927845817, (50, 6615): 444.3616748571774, (50, 6616): 445.49102982304396, (50, 6617): 444.99903466747895, (50, 6618): 446.5827885813641, (50, 6619): 443.4254792120682, (50, 6620): 445.550572977667, (50, 6621): 444.6891639290246, (50, 6622): 444.8657609928753, (50, 6623): 444.0948624567748, (50, 6624): 443.3526260099548, (50, 6625): 443.1722196393298, (50, 6626): 443.3661726324698, (50, 6627): 443.92559997381187, (50, 6628): 445.41269925810275, (50, 6629): 443.6377485042058, (50, 6630): 442.3803197297901, (50, 6632): 443.52817351231414, (50, 6634): 441.4564714928311, (50, 6635): 444.3553490951458, (50, 6636): 445.5524895864307, (50, 6637): 442.44712031520635, (50, 6638): 442.51133329658336, (50, 6639): 444.0283149429496, (50, 6640): 442.64412763266915, (50, 6641): 444.699639395901, (50, 6642): 442.551040221225, (50, 6643): 443.25176160698334, (50, 6645): 443.5592331692299, (50, 6646): 446.2385923063507, (50, 6647): 442.8022429362514, (50, 6653): 444.3142937982995, (50, 6655): 444.03097134549046, (50, 6658): 441.4024956084373, (50, 6662): 442.523790740943, (50, 6819): 393.4709087279003, (50, 6996): 412.203272763323, (50, 7059): 423.7975411186345, (50, 7187): 411.47123879655214, (50, 7304): 381.9077783712906, (50, 7528): 413.9199246193661, (50, 7720): 480.53599145534054, (50, 7793): 480.0983032181326, (50, 7807): 480.7130663147578, (50, 7808): 479.9968831990277, (50, 7831): 450.93358663431604, (50, 7850): 461.7273014877518, (50, 7852): 459.125793179332, (50, 8012): 476.05108247926984, (50, 8125): 493.2784837862653, (50, 8208): 502.003018216766, (50, 8392): 460.9818318980616, (50, 8651): 337.66332170574645, (50, 9088): 388.7564132458889, (50, 9443): 322.3979718569164, (50, 9444): 324.2886123728523, (50, 9828): 283.4679612350248, (50, 9868): 272.00482263687195, (50, 10180): 494.99319766211147, (50, 10256): 525.1943569179947, (50, 10276): 510.2525272868605, (50, 10378): 510.95471841737316, (50, 10676): 490.7381583034532, (50, 10714): 473.04893893455693, (50, 10730): 472.00599996790424, (50, 10862): 503.7666969926285, (50, 10881): 508.42161365614544, (50, 10883): 507.9451180378441, (50, 10885): 502.7556499501349, (50, 10891): 507.214309392499, (50, 10909): 506.7107602496422, (50, 10911): 507.26806486732056, (50, 10913): 506.2242951631014, (50, 10915): 506.12692203308825, (50, 10919): 506.734122854291, (50, 11037): 476.903016874936, (50, 11039): 464.4834478109674, (50, 11516): 770.6728325890862, (50, 11856): 654.2344196420478, (50, 11857): 653.6176681440749, (50, 11861): 653.9762257699304, (50, 11881): 652.1505365288324, (50, 11902): 647.0862315872154, (50, 11911): 645.7188333292306, (50, 11914): 646.6191605843445, (50, 11922): 650.5387939430739, (50, 11924): 651.6168327560648, (50, 11926): 650.1313962259338, (50, 11950): 652.5138200099497, (50, 11963): 657.351198234308, (50, 11983): 653.2594473111429, (50, 11985): 659.8200630031373, (50, 12009): 658.1595084276022, (50, 12010): 654.9095304979169, (50, 12018): 655.3762203340988, (50, 12020): 656.4108631175452, (50, 12021): 656.8985068607931, (50, 12024): 660.1716952145238, (50, 12025): 659.2131465872975, (50, 12027): 658.401551964735, (50, 12031): 654.340878766405, (50, 12032): 655.5942911281907, (50, 12035): 657.7737444844189, (50, 12041): 660.6525070229742, (50, 12045): 614.4693806926617, (50, 12145): 634.6377704087699, (50, 12275): 711.1329440398017, (50, 12294): 701.4505291393289, (50, 12358): 727.7009103445506, (50, 12463): 737.3111792911806, (50, 12465): 736.9462802066535, (50, 12482): 742.3234710066945, (50, 12503): 741.4906728454879, (50, 12506): 742.7660810364223, (50, 12549): 740.9007160076163, (50, 12559): 739.7486856792134, (50, 12569): 740.4766968778614, (50, 12572): 741.4541411964622, (50, 12574): 739.5102600553992, (50, 12576): 742.117974715038, (50, 12591): 742.4036178268087, (50, 12608): 750.5502057888715, (50, 12696): 738.4422573309132, (50, 12710): 746.4058233010561, (50, 12728): 742.121930563001, (50, 12766): 535.6778147530507, (50, 12771): 528.2527241849602, (50, 12790): 526.9548643092357, (50, 12795): 523.7470059328778, (50, 12797): 513.1085485981916, (50, 12798): 514.7896594309536, (50, 12811): 524.0297933388402, (50, 12830): 520.5813145295807, (50, 12848): 522.9066780682773, (50, 12850): 524.1195707848509, (50, 12852): 520.3527166546868, (50, 12854): 518.9276758012295, (50, 12859): 524.512484813117, (50, 12861): 516.5260907098123, (50, 12865): 525.4700296179421, (50, 12866): 524.9429875200965, (50, 12867): 527.6139429130724, (50, 12874): 526.2891822333625, (50, 12875): 527.4566420486524, (50, 12881): 522.794930839404, (50, 12883): 524.5828959229549, (50, 12885): 528.3464375960319, (50, 12888): 523.9010276246145, (50, 12889): 523.6377867819914, (50, 12892): 526.5162088850833, (50, 12893): 523.8243853024635, (50, 12896): 524.8183411948245, (50, 12906): 525.7656980518991, (50, 13018): 509.5893236167419, (50, 13071): 509.0839055810116, (50, 13131): 500.2928189359303, (50, 13146): 510.3940020559868, (50, 13159): 493.7302894919521, (50, 13193): 498.6665163420838, (50, 13198): 483.2952833097823, (50, 13292): 502.7767891711669, (50, 13296): 509.64497108434614, (50, 13406): 470.86412292175953, (50, 13407): 470.1654888922967, (50, 13417): 467.7662469720534, (50, 13418): 469.4000502830302, (50, 13438): 477.6061293417503, (50, 13442): 479.44534652257096, (50, 13443): 477.98394820725713, (50, 13764): 350.16604306192585, (50, 13766): 352.0044773645803, (50, 13771): 350.2757238755581, (50, 13783): 348.56859414993454, (50, 13784): 353.9894259442337, (50, 13792): 346.88105800625715, (50, 13824): 347.3094937458127, (50, 14017): 358.4389481545198, (50, 14870): 501.9560430030395, (50, 14997): 403.81618118778886, (50, 15000): 404.5566767965234, (50, 15003): 406.34794190113433, (50, 15006): 406.6381751712547, (50, 15007): 407.93346312470453, (50, 15056): 409.42542399531914, (50, 15063): 408.6520147389385, (50, 15069): 408.8881999761303, (50, 15076): 408.51431894519396, (50, 15086): 403.92932914791993, (50, 15087): 403.3521845831079, (50, 15111): 399.08729457567284, (50, 15116): 401.5912336670121, (50, 15722): 368.36244961999955, (50, 15998): 363.1950699398237, (50, 16073): 136.40073780053814, (50, 16939): 129.60615805757624, (50, 16940): 128.81379442886765, (50, 16951): 127.08168141778397, (50, 16963): 127.80834269358377, (50, 16965): 129.97780205053107, (50, 16969): 128.09529824832734, (50, 16970): 129.101919425297, (50, 16971): 127.25127350184455, (50, 16973): 126.17932990874641, (50, 16974): 129.95800696826856, (50, 16976): 129.8449610377973, (50, 16978): 128.82823113224867, (50, 16980): 131.33776246950802, (50, 16982): 128.9764600240491, (50, 17045): 150.12310066510992, (50, 17048): 152.68160995955674, (50, 17304): 694.3907584626525, (50, 17305): 692.4602224063076, (50, 17330): 693.8478635303993, (50, 17334): 692.1233422676561, (50, 17343): 695.5009780710451, (50, 17345): 691.2991406945299, (50, 17347): 693.2017927690002, (50, 17351): 688.8744093439815, (50, 17372): 691.5781096372248, (50, 17373): 695.4726533744952, (50, 17377): 695.6859082652269, (50, 17382): 692.9939807112991, (50, 17383): 693.740996770362, (50, 17389): 692.0926021516298, (50, 17400): 694.9537143443454, (50, 17401): 695.016668302824, (50, 17402): 695.042037682943, (50, 17403): 695.2508665426461, (50, 17440): 690.6640055726783, (50, 17455): 694.543669085235, (50, 17491): 694.255487035745, (50, 17507): 692.1996716575278, (50, 17509): 693.9129423192982, (50, 17590): 687.0298363624958, (50, 17615): 683.273504742551, (50, 17642): 684.4369558502192, (50, 17643): 684.0209239211248, (50, 17668): 683.3890746332453, (50, 17721): 681.3768784453756, (50, 17754): 696.2864623546442, (50, 17769): 693.5420641015144, (50, 17776): 686.1032590828968, (50, 17804): 696.164222307705, (50, 17809): 697.7075163481738, (50, 17824): 697.1653168142321, (50, 17837): 690.5125426525198, (50, 17838): 690.2624943058426, (50, 17862): 688.9158054538037, (50, 17866): 692.3968286679827, (50, 17872): 688.0625570073905, (50, 17873): 685.3093910469061, (50, 17881): 689.471516380814, (50, 17947): 171.8720419906002, (50, 17951): 171.06397037079253, (50, 17953): 172.03176510843994, (50, 17954): 172.8132033907553, (50, 17959): 169.77257263904156, (50, 17963): 167.55327914454097, (50, 18000): 167.9558880571405, (50, 18001): 169.41393501782767, (50, 18111): 228.97202855705825, (50, 18148): 228.17009589657968, (50, 18166): 230.1718534709718, (50, 18189): 224.37708081359608, (50, 18239): 696.5348542819278, (50, 18240): 696.4245165013781, (50, 18245): 696.6314498912649, (50, 18247): 696.1959688783205, (50, 18251): 696.513676208592, (50, 18256): 696.7508288457655, (50, 18258): 696.3106181255336, (50, 18259): 696.3307205708003, (50, 18260): 696.411586345763, (50, 18262): 696.633202911308, (50, 18263): 696.7999116716461, (50, 18264): 696.8862455857046, (50, 18266): 696.6658586230988, (50, 18267): 696.7633236288344, (50, 18268): 696.776791729983, (50, 18269): 696.9612120762241, (50, 18275): 696.8737870329143, (50, 18285): 696.8932250315976, (50, 18308): 694.9455788610181, (50, 18313): 694.0260745501931, (50, 18314): 694.1589768949747, (50, 18315): 697.20685131645, (50, 18316): 697.0649173958609, (50, 18317): 697.143396866934, (50, 18320): 697.3963148080642, (50, 18321): 697.3836704638113, (50, 18322): 697.5324884217566, (50, 18324): 697.8300892195374, (50, 18325): 698.4647221797301, (50, 18326): 698.2339591808615, (50, 18327): 697.1118783281547, (50, 18329): 698.8877320907397, (50, 18330): 698.1860861572803, (50, 18331): 697.822105451654, (50, 18332): 697.3834171252937, (50, 18333): 698.229810901532, (50, 18336): 698.0583897994118, (50, 18337): 698.3528224274327, (50, 18403): 697.3369771353749, (50, 18432): 685.0805298552716, (50, 18451): 693.3690788256848, (50, 18466): 701.7683891356758, (50, 18481): 697.6981918665713, (50, 18483): 697.6113833894796, (50, 18484): 697.3285292904338, (50, 18485): 696.5643017505744, (50, 18486): 697.8074920132345, (50, 18487): 697.0992089090165, (50, 18489): 697.4185998354138, (50, 18490): 698.4626620799336, (50, 18491): 698.8452849067592, (50, 18492): 696.209951686757, (50, 18493): 697.7738489070643, (50, 18494): 697.1934826320563, (50, 18495): 698.1904276092978, (50, 18496): 697.7189367771102, (50, 18497): 697.0153271359375, (50, 18498): 696.8529153272822, (50, 18499): 697.4164747599654, (50, 18501): 697.1601214458361, (50, 18502): 696.8093592441711, (50, 18503): 696.4358762728109, (50, 18504): 697.7713971931289, (50, 18506): 697.4600660535308, (50, 18507): 697.1741320221847, (50, 18508): 697.4211839826891, (50, 18509): 697.5096899051904, (50, 18510): 696.5647887887163, (50, 18511): 698.057294401363, (50, 18512): 697.4681388380347, (50, 18515): 697.9274264443147, (50, 18516): 698.2372991210891, (50, 18517): 697.916473788897, (50, 18518): 698.4607893708587, (50, 18519): 697.8001278616329, (50, 18520): 697.211925063498, (50, 18522): 699.1756760441591, (50, 18523): 699.3497295413866, (50, 18532): 699.9952158789571, (50, 18535): 698.7500209036344, (50, 18537): 698.0567781299616, (50, 18539): 698.2503745853286, (50, 18540): 698.3824684070206, (50, 18541): 698.7661657174293, (50, 18542): 699.0009180321822, (50, 18543): 697.8727523650413, (50, 18546): 698.5663965796595, (50, 18555): 699.6617137809018, (50, 18556): 699.9241291801557, (50, 18565): 700.0395012039869, (50, 18567): 700.5411515949303, (50, 18568): 699.8662829145992, (50, 18577): 704.1107979040743, (50, 18583): 703.1445798523199, (50, 18605): 703.7317568195305, (50, 18608): 701.2754846222912, (50, 18616): 707.7137463840241, (50, 18618): 711.2633470892317, (50, 18625): 709.4332618092383, (50, 18645): 706.1660924324697, (50, 18646): 707.1679021258659, (50, 18653): 704.9865939209068, (50, 18654): 707.7369787923086, (50, 18655): 706.0670821224425, (50, 18666): 715.9382713409365, (50, 18837): 693.9818124968757, (50, 18974): 691.1750747905182, (50, 18999): 692.8810270645469, (50, 19000): 693.8771677199461, (50, 19174): 640.9529094612558, (50, 19342): 659.511426742393, (50, 19455): 652.3536816117132, (50, 19555): 601.0571094836498, (50, 19564): 602.2477025790115, (50, 19573): 600.5025671226615, (50, 19586): 599.8367795375731, (50, 19605): 600.9042404040895, (50, 19611): 602.1477215880312, (50, 19614): 602.0552760527856, (50, 19641): 624.9816798974311, (50, 19702): 624.0457775905207, (50, 19713): 622.4756375382151, (50, 19731): 595.5899236386691, (50, 19819): 643.6870496291247, (50, 19893): 612.9949210625698, (50, 19899): 624.7772346609831, (50, 19929): 615.9180851485463, (50, 19951): 638.762225159912, (50, 19962): 618.1088258186979, (50, 19970): 622.4754215453912, (50, 19971): 622.7306733572268, (50, 19972): 620.9160241640683, (50, 19975): 619.9047904315998, (50, 19978): 642.9774117182104, (50, 19987): 643.2827818782947, (50, 19989): 636.9979512743733, (50, 20039): 644.3968213970396, (50, 20043): 646.9053830106405, (50, 20047): 644.7918998479711, (50, 20052): 637.9341167893103, (50, 20054): 638.537668880415, (50, 20085): 669.3008762055055, (50, 20104): 671.2455473193854, (50, 20132): 659.4475013111097, (50, 20203): 613.0967063959042, (50, 20280): 610.9330750127598, (50, 20285): 610.4518588501847, (50, 20290): 611.9526979125735, (50, 20297): 609.7911834290918, (50, 20309): 645.4895132323653, (50, 20453): 677.2875667722095, (50, 20485): 596.2333357624988, (50, 20520): 590.736695227735, (50, 20526): 589.1332503626116, (50, 20698): 304.2335443656349, (50, 20868): 245.47402915881378, (50, 21042): 533.3129560948438, (50, 21057): 545.7954106262631, (50, 21066): 540.1109562772288, (50, 21075): 537.1338625952508, (50, 21093): 534.8673659113107, (50, 21098): 544.6272329963444, (50, 21127): 534.6663737617031, (50, 21130): 537.3231054723905, (50, 21144): 536.3903169911, (50, 21146): 533.8474817444945, (50, 21147): 536.0093191635629, (50, 21148): 538.381279088649, (50, 21153): 530.9994630073252, (50, 21293): 554.8103284471827, (50, 21426): 546.3907341992722, (50, 21442): 558.8975943312538, (50, 21451): 560.1288155877451, (50, 21466): 552.8647194361729, (50, 21469): 554.9594641710404, (50, 21471): 551.7916248454073, (50, 21473): 553.5835765321297, (50, 21475): 552.047380626419, (50, 21482): 556.0818179036697, (50, 21484): 555.7514614796197, (50, 21488): 554.4685782764932, (50, 21494): 552.3152331481135, (50, 21498): 553.8045657736694, (50, 21500): 551.6704189690837, (50, 21514): 556.8147248245393, (50, 21537): 551.8705010781156, (50, 21662): 559.3904726188954, (50, 21691): 551.4262345037133, (50, 21757): 535.0672515678763, (50, 21777): 511.18545313939785, (50, 21778): 509.1930565712582, (50, 21779): 510.6069306240918, (50, 21790): 513.1063435861377, (50, 21802): 513.5858339887583, (50, 21824): 515.9544290901957, (50, 21874): 511.495000430162, (50, 21879): 510.88191520636093, (50, 21983): 516.285815319539, (50, 22002): 539.7565846267145, (50, 22132): 519.7648040363911, (50, 22261): 300.6974074613485, (50, 22298): 306.52828375491947, (50, 22339): 299.6762177414667, (50, 22508): 328.4051768755101, (50, 22841): 227.2152821039244, (50, 22842): 226.7025168709467, (50, 22874): 220.70996226900047, (50, 22941): 222.92184609342365, (50, 22956): 225.0341135013303, (50, 22960): 227.04479019178262, (50, 22968): 222.69247450889603, (50, 22970): 224.37574212409467, (50, 22974): 221.56826768144967, (50, 22980): 224.73487205860198, (50, 23025): 218.92883238712852, (50, 23028): 217.12443596398984, (50, 23081): 216.69153810852117, (50, 23104): 203.64393829839898, (50, 23147): 187.93896569057736, (50, 23298): 593.1422185775102, (50, 23376): 587.5083499843876, (50, 23381): 585.4528403072563, (50, 23529): 597.8020683622761, (50, 23556): 594.377742613795, (50, 23718): 588.6106977365946, (50, 24001): 626.2775701513981, (50, 24094): 638.9308746890039, (50, 24129): 644.5376328436175, (50, 24174): 633.8077195547907, (50, 24235): 646.8667497736168, (50, 24259): 651.6176841867722, (50, 24260): 651.3080462225612, (50, 24261): 650.0177457995482, (50, 24305): 657.7661767241738, (50, 24306): 658.9732449609432, (50, 24307): 657.2672750918296, (50, 24308): 638.764095280893, (50, 24498): 670.110042422551, (50, 24499): 670.2767653822503, (50, 24500): 669.1906450706666, (50, 24668): 659.8109140575996, (50, 24711): 678.1824615921153, (50, 24756): 682.8749488436143, (50, 24788): 684.0965112683066, (50, 24809): 678.7835559845746, (50, 24813): 680.35645225929, (50, 24821): 679.8004544836725, (50, 24825): 680.3815994074554, (50, 24832): 678.2885415933509, (50, 24833): 679.1958722283968, (50, 24835): 680.1512744631716, (50, 24837): 681.4742158223588, (50, 24840): 678.210575861978, (50, 24841): 679.483141169986, (50, 24844): 678.336679603586, (50, 24845): 678.8321979739083, (50, 24846): 679.2196152269387, (50, 24849): 679.7547819983181, (50, 24850): 680.7368182067745, (50, 24863): 667.5077612736114, (50, 24866): 669.0967698347396, (50, 24885): 671.3018039470214, (50, 24886): 671.6272936436837, (50, 24889): 674.5103515257846, (50, 24903): 675.5908229245049, (50, 24909): 669.2346642899637, (50, 24999): 737.1661496410128, (50, 25019): 734.5692554141101, (50, 25028): 736.3741260606032, (50, 25137): 617.218424000362, (50, 25145): 619.4055654416444, (50, 25208): 646.601804603633, (50, 25233): 643.6968117233147, (50, 25371): 616.016949651995, (50, 25377): 609.3437756903932, (50, 25828): 495.5563046211421, (50, 25851): 476.9092790625183, (50, 25874): 493.7096134151203, (50, 25898): 502.51419217167967, (50, 25946): 493.71058667264793, (50, 26047): 532.4125841605687, (50, 26066): 566.8796001766541, (50, 26197): 543.485517748084, (50, 26212): 446.8566879535029, (50, 26253): 442.15825829182546, (50, 26254): 443.689481054619, (50, 26257): 446.15228465262095, (50, 26258): 443.33886116165127, (50, 26260): 444.7234309392841, (50, 26266): 441.05281043522274, (50, 26267): 442.9886143810126, (50, 26271): 443.2758411830471, (50, 26304): 459.36035904133234, (50, 26305): 458.6523439305203, (50, 26363): 491.86547131027476, (50, 26441): 349.1260288123697, (50, 26442): 348.5382234857827, (50, 26450): 350.2224777253494, (50, 26459): 354.05324585664823, (50, 26462): 355.4657356816898, (50, 26467): 351.3689400889987, (50, 26471): 350.59442593305545, (50, 26472): 350.1601946915562, (50, 26473): 349.6704503485347, (50, 26476): 344.8300224723996, (50, 26485): 351.483523120809, (50, 26493): 349.52726929288866, (50, 26524): 356.50204503013117, (50, 26525): 355.6450734546611, (50, 26556): 351.3318660522777, (50, 26560): 354.6016006316781, (50, 26561): 356.209763492608, (50, 26564): 350.85995075315515, (50, 26569): 355.39553455457, (50, 26570): 354.5635849035212, (50, 26573): 352.67130251588947, (50, 26581): 351.2272689193487, (50, 26583): 352.4579762470134, (50, 26593): 349.34945381107485, (50, 26837): 349.56889170139465, (50, 26844): 349.36261061248985, (50, 26863): 346.18528801361646, (50, 26893): 344.0074364883971, (50, 26902): 343.5988786070688, (50, 26905): 347.3143166840672, (50, 26912): 345.95569452376515, (50, 26921): 345.3564435400014, (50, 26922): 341.1673174278173, (50, 27212): 423.6114630868618, (50, 27218): 427.06569119019457, (50, 27239): 422.66496407918027, (50, 27257): 421.62452609722015, (50, 27274): 421.9587601669907, (50, 27279): 420.6940819255853, (50, 27282): 420.91561073160636, (50, 27283): 423.31733453712354, (50, 27285): 421.09544227322226, (50, 27286): 419.04712859384125, (50, 27290): 420.90553632164904, (50, 27295): 422.9582191865617, (50, 27300): 422.4308824345964, (50, 27344): 417.26554566077306, (50, 27366): 415.7273599638184, (50, 27383): 418.3778797080788, (50, 27398): 421.28327757393726, (50, 27406): 422.4122899615431, (50, 27407): 423.3879283535937, (50, 27426): 432.3255411917192, (50, 27432): 430.55206995778747, (50, 27460): 432.80021644540676, (50, 27523): 395.5978734061905, (50, 27545): 416.13853233925005, (50, 27602): 408.7230919595528, (50, 27606): 410.4822635991848, (50, 27646): 384.8820320996179, (50, 27667): 383.25339399650625, (50, 27672): 384.1984048033638, (50, 27674): 383.819036197882, (50, 27688): 387.6344528519553, (50, 27692): 382.77384148618216, (50, 27693): 382.77929515071725, (50, 27705): 381.62668935143967, (50, 27712): 380.6376352406898, (50, 27786): 450.3589041877046, (50, 27790): 463.7994041540025, (50, 27791): 465.76600919821635, (50, 27795): 448.870859066227, (50, 27801): 457.63597825774383, (50, 27813): 448.8999307135632, (50, 27816): 451.5263362816936, (50, 27823): 458.09280843345925, (50, 27830): 454.54079107623556, (50, 27884): 376.6768117227995, (50, 27885): 383.85728654374776, (50, 27896): 380.0303247711235, (50, 27919): 380.8572637388082, (50, 27922): 380.12201940812525, (50, 27930): 379.12144267965215, (50, 27934): 378.413042027932, (50, 27935): 377.49440073751265, (50, 27948): 354.2974894986764, (50, 27951): 372.220098952543, (50, 28061): 236.14371514128317, (50, 28290): 246.66100065254685, (50, 28292): 241.93418031910454, (50, 28293): 245.3209431844981, (50, 28295): 241.76402315449042, (50, 28296): 244.85107926331455, (50, 28297): 248.8051115545263, (50, 28302): 245.6203537892105, (50, 28310): 24.0, (50, 28313): 24.0, (50, 28372): 24.0, (50, 28398): 24.0, (50, 28399): 24.0, (50, 28400): 24.0, (50, 28401): 24.0, (50, 28445): 24.0, (50, 28475): 24.0, (50, 28885): 648.8889977893587, (50, 28886): 647.880835379394, (50, 28915): 649.0697639959781, (50, 28916): 648.0777005464219, (50, 28917): 647.552681156319, (50, 28921): 650.8297572266345, (50, 28931): 650.6084853149656, (50, 28945): 646.1805820411082, (50, 28982): 647.1837840930075, (50, 29219): 654.7307699672081, (50, 29228): 649.8362285623983, (50, 29246): 682.2736318532682, (50, 29248): 682.0956852209406, (50, 29282): 675.4140676791561, (50, 29290): 685.2467003219282, (50, 29291): 683.9926915254092, (50, 29292): 685.2048320668679, (50, 29293): 682.606280588321, (50, 29294): 684.7852391250344, (50, 29298): 682.8725949001673, (50, 29299): 682.720927966092, (50, 29304): 680.1369715069055, (50, 29317): 673.8077154277149, (50, 29323): 673.3081794591034, (50, 29330): 676.3699558480246, (50, 29331): 677.8312690954746, (50, 29344): 655.831625338145, (50, 29445): 600.9986777125472, (50, 29724): 242.86383718852096, (50, 29738): 243.55572567838328, (50, 29745): 242.46503707064687, (50, 29748): 247.59765607743532, (50, 29750): 250.7208176800372, (50, 29759): 246.08453949194762, (50, 29772): 248.6658448833628, (50, 29781): 248.23711540970424, (50, 29784): 245.75824829299344, (50, 29790): 249.6389937843574, (50, 29811): 250.30760470389532, (50, 29817): 267.78576532081985, (50, 29818): 267.4814149747065, (50, 29929): 239.31832621350952, (50, 30039): 236.58225281397674, (50, 30066): 223.72771737493596, (50, 30116): 208.8086740969949, (50, 30238): 195.33929266567867, (50, 30248): 185.6953809164196, (50, 30260): 184.62893311502225, (50, 30545): 631.179386128959, (50, 30733): 578.0015584032965, (50, 30756): 566.7528246584465, (50, 30921): 590.9866407175033, (50, 31079): 441.729741334309, (50, 31149): 438.2101798382823, (50, 31154): 437.78137246104916, (50, 31160): 437.89840387599804, (50, 31163): 436.99498512324095, (50, 31189): 417.6171456909611, (50, 31215): 418.1945435208145, (50, 31259): 413.01419545693847, (50, 31262): 411.0605611363541, (50, 31430): 442.2874857824947, (50, 31568): 380.210789417402, (50, 31751): 429.34052797133097, (53, 109): 711.8687094809355, (53, 872): 232.07975931413333, (53, 873): 230.04278050134894, (53, 877): 229.7995074520544, (53, 879): 229.39874493055532, (53, 884): 229.22921375732136, (53, 889): 228.40986624673494, (53, 891): 230.17787345567984, (53, 892): 228.0276467149709, (53, 894): 228.69847214090817, (53, 896): 232.3354578099782, (53, 903): 228.5776658530682, (53, 909): 235.3446071571192, (53, 910): 235.46196252810518, (53, 912): 236.5873531758674, (53, 913): 237.4934110977282, (53, 916): 239.23048445617363, (53, 926): 236.03111753039278, (53, 927): 236.91918740308623, (53, 948): 231.085912735331, (53, 961): 233.91056902060967, (53, 962): 234.33252084186063, (53, 963): 234.59850483045244, (53, 967): 228.11976240052874, (53, 974): 226.890065196977, (53, 998): 226.48467046589283, (53, 1014): 198.5568186777291, (53, 1086): 265.0431290785178, (53, 1087): 268.8677527054931, (53, 1089): 268.66730513545286, (53, 1090): 267.603002619513, (53, 1092): 264.9688153541603, (53, 1097): 266.26923143911125, (53, 1107): 265.96339389728826, (53, 1387): 591.9041483892516, (53, 1554): 619.6718824829828, (53, 1827): 124.43516190714938, (53, 1828): 124.87798569195088, (53, 1829): 124.24873755548631, (53, 1830): 121.67804615061647, (53, 1831): 122.04418894824954, (53, 1832): 122.47294079845625, (53, 1833): 122.9354965279009, (53, 1836): 123.64551178259381, (53, 1841): 122.0024135726999, (53, 1843): 122.39355819136468, (53, 1844): 121.74151599318, (53, 1845): 121.79173844616827, (53, 1847): 124.73338571059223, (53, 1848): 124.02909232609146, (53, 1849): 120.29516885166268, (53, 1850): 120.40481117721072, (53, 1851): 122.21995920485429, (53, 1852): 121.07074954486788, (53, 1854): 121.60521525013316, (53, 1856): 123.37921338257277, (53, 1857): 123.47506574679315, (53, 1858): 121.38050007894839, (53, 1861): 123.33392919587243, (53, 1866): 122.47594015236689, (53, 1867): 122.91476083316587, (53, 1868): 124.13715152862713, (53, 1870): 120.35656190153551, (53, 1871): 123.92334074129622, (53, 1875): 122.3851121832344, (53, 1880): 123.93766710249425, (53, 1882): 122.1697036580617, (53, 1883): 121.65221007033509, (53, 1889): 125.44554762444636, (53, 1893): 126.03751328383467, (53, 1894): 126.74927925244756, (53, 1899): 126.55860737382939, (53, 1900): 126.64002724850032, (53, 1902): 125.35849627556135, (53, 1905): 124.12424872235124, (53, 1907): 124.74973726253181, (53, 1910): 125.92982033583735, (53, 1917): 126.76376603571299, (53, 1920): 125.68777988923955, (53, 1935): 126.21449953262288, (53, 1937): 125.42509751811502, (53, 1946): 129.95002347275906, (53, 1949): 130.0605081385257, (53, 1950): 128.89198586667487, (53, 1951): 128.83698348159152, (53, 1952): 125.41259947104285, (53, 1953): 127.79528636848653, (53, 1954): 126.22903026265014, (53, 1958): 128.99209928671226, (53, 1960): 127.52208549953099, (53, 1968): 126.94986975394268, (53, 1969): 128.30747720466755, (53, 1974): 127.74015519024633, (53, 1975): 127.01453438700666, (53, 1979): 129.3863841170626, (53, 1980): 127.28831505969217, (53, 1981): 128.37913736758296, (53, 1985): 128.76063628380726, (53, 1994): 124.6279910525752, (53, 2011): 121.45906041842774, (53, 2019): 114.87273595496089, (53, 2020): 115.7188133013708, (53, 2029): 116.8679420789062, (53, 2030): 116.34078336424619, (53, 2032): 115.98893771888739, (53, 2033): 116.41219299068175, (53, 2034): 115.36833091999799, (53, 2036): 112.62512998848554, (53, 2037): 113.47363647057627, (53, 2038): 118.24280680298578, (53, 2042): 111.92066365598238, (53, 2050): 118.24400298439363, (53, 2051): 117.19599494793947, (53, 2053): 117.52491257518795, (53, 2054): 116.91521446147195, (53, 2066): 117.95956492728254, (53, 2067): 118.53903486655885, (53, 2071): 126.30555981665438, (53, 2072): 126.07217704021546, (53, 2073): 131.82541542481215, (53, 2074): 131.26575634112217, (53, 2080): 131.32104246973958, (53, 2082): 125.7042206497494, (53, 2083): 125.66617841293055, (53, 2089): 127.54224115826284, (53, 2090): 127.6965683603398, (53, 2092): 128.9598644309357, (53, 2098): 132.03766377442324, (53, 2099): 130.7903205222649, (53, 2101): 131.18693571957417, (53, 2102): 129.7117959050162, (53, 2103): 129.7657658139293, (53, 2104): 129.34555697849058, (53, 2106): 124.8946241798496, (53, 2112): 130.0861769025847, (53, 2113): 128.90951648355482, (53, 2114): 126.87569270424129, (53, 2117): 123.81441806629884, (53, 2123): 165.83842448275428, (53, 2124): 165.65089591460386, (53, 2134): 163.50617665459038, (53, 2138): 164.0056717870254, (53, 2141): 164.26335297640992, (53, 2148): 153.54780570768992, (53, 2150): 164.2741149792577, (53, 2151): 163.28674987102485, (53, 2152): 163.68881563499184, (53, 2153): 154.462458817204, (53, 2154): 156.05965426469933, (53, 2155): 154.4401701854678, (53, 2156): 155.86970558317162, (53, 2157): 149.30296417488964, (53, 2160): 158.67898931910335, (53, 2161): 162.70057355333242, (53, 2162): 150.49143613344182, (53, 2163): 151.16652042855765, (53, 2164): 150.56238365909527, (53, 2168): 158.8741213396633, (53, 2172): 153.92744870708765, (53, 2174): 162.0060577304187, (53, 2178): 152.34615693843665, (53, 2179): 152.1120336698302, (53, 2183): 162.80364765930958, (53, 2185): 162.14287296619526, (53, 2186): 162.64279816340184, (53, 2190): 159.78909337332385, (53, 2192): 160.46379952885857, (53, 2193): 163.1128288259437, (53, 2194): 163.79651966284894, (53, 2195): 162.50915194391172, (53, 2197): 159.63599900130586, (53, 2205): 158.65637464383215, (53, 2207): 157.86862947490542, (53, 2208): 158.0281970948829, (53, 2212): 165.9744922333613, (53, 2214): 157.94222724872733, (53, 2225): 152.561135511789, (53, 2231): 183.12329947989517, (53, 2278): 136.80559632544205, (53, 2284): 133.16534230620726, (53, 2285): 132.52455570734327, (53, 2291): 130.13964058453496, (53, 2292): 136.46332943486888, (53, 2307): 134.00100881019418, (53, 2313): 128.4851653912458, (53, 2317): 140.37587945939913, (53, 2319): 135.24492294065126, (53, 2321): 133.38961897661957, (53, 2323): 135.3966194133523, (53, 2326): 136.30608959202803, (53, 2327): 136.96425069335174, (53, 2329): 137.2165321143787, (53, 2330): 137.05184906355888, (53, 2332): 135.03276734405455, (53, 2344): 139.54047969411272, (53, 2346): 138.22005821059747, (53, 2361): 149.87097147283245, (53, 2368): 136.04056529503305, (53, 2374): 134.3031419200774, (53, 2375): 134.8033979757496, (53, 2377): 138.1343384449665, (53, 2378): 133.788373419792, (53, 2379): 132.29282322559763, (53, 2380): 133.08961497209074, (53, 2383): 138.37342251247236, (53, 2385): 138.51302596157157, (53, 2395): 139.74288278102728, (53, 2397): 131.91906926987414, (53, 2398): 139.0576000777107, (53, 2399): 138.83055063857023, (53, 2400): 139.05650493242874, (53, 2402): 133.69130307739078, (53, 2403): 133.04602560166288, (53, 2404): 133.4657031049505, (53, 2405): 134.49945915731433, (53, 2407): 134.50219364092442, (53, 2408): 133.14723624284596, (53, 2409): 134.40403512973486, (53, 2411): 130.6830192723326, (53, 2412): 131.73976474275514, (53, 2413): 130.8847048152549, (53, 2414): 131.4278018015508, (53, 2422): 130.05724560019917, (53, 2424): 132.0767637370001, (53, 2426): 132.4200400508419, (53, 2433): 132.68256953942074, (53, 2436): 131.46211100716567, (53, 2437): 135.7407997648284, (53, 2440): 135.1983147078765, (53, 2445): 106.57168817807901, (53, 2447): 109.7169591772037, (53, 2454): 108.11757197819814, (53, 2455): 109.21337251703225, (53, 2460): 112.8101907369081, (53, 2461): 112.07677776276684, (53, 2471): 95.98394314637122, (53, 2492): 64.73700512125066, (53, 2511): 78.42311393893782, (53, 2523): 71.29297369497483, (53, 2525): 70.48837289959108, (53, 2535): 89.23704019520017, (53, 2537): 89.96282808948244, (53, 2538): 90.51485187563972, (53, 2539): 85.75235374838344, (53, 2540): 88.78886156033536, (53, 2542): 86.45435054300773, (53, 2559): 85.87643370042697, (53, 2575): 79.38519459685057, (53, 2599): 116.30161670614889, (53, 2600): 106.93678764132709, (53, 2607): 116.3633337083148, (53, 2627): 58.412156066353674, (53, 2647): 50.88462759077857, (53, 2674): 57.67821865066632, (53, 2681): 56.23951322109513, (53, 2683): 54.840604273244665, (53, 2686): 58.54334622961495, (53, 2689): 31.05041803294047, (53, 2690): 30.22869777687928, (53, 2713): 24.0, (53, 2714): 24.0, (53, 2715): 24.0, (53, 2739): 24.0, (53, 2740): 24.0, (53, 2741): 24.0, (53, 2749): 24.0, (53, 2750): 24.0, (53, 2752): 24.0, (53, 2755): 24.0, (53, 2758): 24.0, (53, 2759): 24.0, (53, 2769): 24.0, (53, 2771): 24.0, (53, 2779): 24.0, (53, 2784): 24.0, (53, 2800): 24.0, (53, 2802): 24.0, (53, 2803): 24.0, (53, 2804): 24.0, (53, 2805): 24.0, (53, 2807): 24.0, (53, 2809): 24.0, (53, 2812): 24.0, (53, 2814): 24.0, (53, 2817): 24.0, (53, 2819): 24.0, (53, 2823): 24.0, (53, 2832): 24.0, (53, 2836): 24.0, (53, 2839): 24.0, (53, 2841): 24.0, (53, 2843): 24.0, (53, 2846): 24.0, (53, 2849): 24.0, (53, 2852): 24.0, (53, 2853): 24.0, (53, 2876): 24.0, (53, 2877): 24.0, (53, 2885): 24.0, (53, 2918): 24.0, (53, 2921): 24.0, (53, 2925): 24.773357614855612, (53, 2926): 30.308840412955377, (53, 2930): 24.0, (53, 2931): 24.0, (53, 2938): 24.0, (53, 2940): 24.0, (53, 2947): 24.0, (53, 2949): 24.0, (53, 2950): 24.0, (53, 2952): 24.0, (53, 2958): 24.0, (53, 2959): 24.0, (53, 2960): 24.0, (53, 2961): 24.0, (53, 2963): 24.0, (53, 2968): 24.0, (53, 2976): 24.0, (53, 2981): 24.0, (53, 2982): 24.0, (53, 2984): 24.0, (53, 3003): 24.0, (53, 3046): 39.448872057812544, (53, 3050): 27.708069972945456, (53, 3051): 27.514537216192096, (53, 3053): 28.592127650249267, (53, 3069): 24.0, (53, 3071): 30.98162483761427, (53, 3080): 24.0, (53, 3199): 29.46763050472264, (53, 3200): 31.488202151074344, (53, 3205): 24.0, (53, 3209): 30.90105655017522, (53, 3215): 30.869847097645355, (53, 3217): 32.71474999558078, (53, 3249): 30.172894609542613, (53, 3263): 24.0, (53, 3289): 24.397025366538248, (53, 3301): 25.217521830941127, (53, 3302): 25.382886983668907, (53, 3307): 26.085451174196585, (53, 3310): 24.43662580560159, (53, 3391): 70.34412782958384, (53, 3509): 337.39618742714106, (53, 3510): 338.7875173576834, (53, 3511): 337.9666531723091, (53, 3512): 338.9240540245839, (53, 3514): 338.7232435520858, (53, 3519): 333.6910059654409, (53, 3536): 335.13304791198755, (53, 3545): 333.0694244262191, (53, 3548): 335.3615805622438, (53, 3572): 334.2093376812393, (53, 3581): 335.5700023531167, (53, 3583): 336.92638723724554, (53, 3601): 330.96252863377396, (53, 3656): 333.0021431249226, (53, 3669): 335.5211402110638, (53, 3670): 334.2715132328228, (53, 3695): 341.44516943424014, (53, 3696): 340.46077887513525, (53, 3782): 337.8940487872459, (53, 3792): 338.83778018457167, (53, 3989): 922.3058469462235, (53, 4008): 929.1285063613562, (53, 4031): 927.4430345062387, (53, 4045): 926.2060053936102, (53, 4144): 927.7237830427019, (53, 4145): 922.0802512735951, (53, 4164): 925.3746081807165, (53, 4168): 923.8126688542247, (53, 4173): 923.6596845385523, (53, 4181): 919.4816164347848, (53, 4228): 914.2547053349441, (53, 4248): 914.2618382491614, (53, 4254): 881.4049268624559, (53, 4260): 881.0743345614303, (53, 4262): 883.8187281525571, (53, 4273): 882.9850178032937, (53, 4319): 862.11507220357, (53, 4326): 861.2565795104796, (53, 4328): 861.4492408111092, (53, 4334): 863.2068910368619, (53, 4335): 862.7230235702522, (53, 4372): 837.9674406778818, (53, 4413): 859.1854734187208, (53, 4434): 837.3431691751309, (53, 4447): 841.2204499660795, (53, 4452): 837.5058721384992, (53, 4463): 785.3739974101512, (53, 4465): 787.3346982248746, (53, 4619): 858.4960015876034, (53, 4645): 864.2651874343636, (53, 4657): 863.0046714913849, (53, 4666): 860.5774851030287, (53, 4676): 864.2510833060809, (53, 4678): 865.2781625299986, (53, 4689): 862.2528122043566, (53, 4704): 880.4130485578025, (53, 4726): 913.9477522961978, (53, 4727): 913.2862317378906, (53, 4730): 912.0412042468251, (53, 4731): 912.1473165968782, (53, 4734): 914.3029381768728, (53, 4735): 913.4603846879808, (53, 4736): 913.5902350510097, (53, 4737): 912.2224744284259, (53, 4738): 912.2199491953246, (53, 4756): 912.7669940143044, (53, 4760): 910.4956355824185, (53, 4761): 911.2921804404666, (53, 4762): 909.3330177102824, (53, 4765): 910.6960127388284, (53, 4773): 915.4612128900598, (53, 4774): 914.5007236984474, (53, 4790): 915.0768103730118, (53, 4795): 914.5911248272937, (53, 4799): 914.5905827870037, (53, 4801): 915.4677401787054, (53, 4804): 915.2777306581983, (53, 4805): 914.8727320727891, (53, 4806): 913.7030101162314, (53, 4815): 912.742622085652, (53, 4816): 914.5682456483585, (53, 4817): 914.4673912434762, (53, 4826): 913.6128794929733, (53, 4830): 912.490772256845, (53, 4839): 912.4062782218023, (53, 4840): 912.817611820367, (53, 4841): 911.2742906950222, (53, 4846): 910.8858080820254, (53, 4848): 910.3723574966735, (53, 4850): 910.9126535110369, (53, 4871): 904.8657990010952, (53, 4883): 910.2740490431321, (53, 4900): 907.9972487633833, (53, 4901): 906.8853315521715, (53, 4917): 851.3063165764764, (53, 4931): 846.0328619549389, (53, 4944): 852.1765093254182, (53, 4956): 846.7282092540665, (53, 4958): 846.0371481344017, (53, 4959): 844.6667144257282, (53, 4961): 848.015722366578, (53, 4966): 845.1276111351035, (53, 5207): 839.229076221344, (53, 5272): 754.3290805939756, (53, 5283): 756.1148882943281, (53, 5287): 757.8730467261695, (53, 5289): 758.6140303495764, (53, 5293): 755.7139599264304, (53, 5295): 760.8710692357615, (53, 5296): 760.1736204106531, (53, 5298): 759.7429147403329, (53, 5303): 760.6947872443716, (53, 5305): 751.9789583770529, (53, 5306): 749.6073991297591, (53, 5307): 750.9708838910097, (53, 5308): 752.6047718436415, (53, 5313): 753.3662685154811, (53, 5314): 754.7740804236298, (53, 5317): 752.1803251814987, (53, 5319): 758.7616524747489, (53, 5324): 758.2317966328284, (53, 5326): 757.9284674159682, (53, 5348): 748.6054561082383, (53, 5351): 749.0169034738755, (53, 5399): 758.6720236476908, (53, 5413): 749.8484711566622, (53, 5422): 760.3331817152751, (53, 5445): 755.8284249614776, (53, 5448): 754.0643885682093, (53, 5456): 752.9392645136195, (53, 5467): 754.3883114067344, (53, 5624): 737.2559605399066, (53, 5671): 803.5899794910167, (53, 5672): 801.236530384781, (53, 5797): 832.1052868438359, (53, 5871): 776.9896092119066, (53, 5976): 755.8863010010076, (53, 6118): 186.16821137007244, (53, 6248): 180.84893913367037, (53, 6345): 649.5423274576107, (53, 6352): 643.0608361215689, (53, 6354): 651.1081641799677, (53, 6359): 652.4237973978229, (53, 6376): 644.1919516574773, (53, 6378): 650.3430576132458, (53, 6381): 651.9190550139656, (53, 6383): 648.1524654332476, (53, 6396): 651.3568003662244, (53, 6399): 649.6697487424731, (53, 6408): 643.2562394183213, (53, 6409): 646.2231810950501, (53, 6419): 635.6267431307531, (53, 6422): 644.0367587531405, (53, 6423): 643.5083346293508, (53, 6424): 650.3865805015646, (53, 6439): 649.1206872248441, (53, 6464): 647.3031219755857, (53, 6465): 646.6736594839, (53, 6469): 647.5335752397044, (53, 6470): 647.1488842808651, (53, 6472): 654.634974499345, (53, 6480): 653.17096122044, (53, 6486): 657.0049854082596, (53, 6497): 655.707593082297, (53, 6503): 647.7039687144071, (53, 6508): 648.1644743762843, (53, 6509): 649.4234961768533, (53, 6521): 653.957991100016, (53, 6544): 653.5056528614562, (53, 6552): 645.0709302732408, (53, 6553): 644.0569146665105, (53, 6554): 643.0253955424745, (53, 6578): 646.7681154884323, (53, 6582): 646.0108103192971, (53, 6601): 647.2291325574855, (53, 6609): 655.4074866920995, (53, 6610): 655.6915831614447, (53, 6611): 655.9072198971033, (53, 6614): 655.3900749816956, (53, 6615): 655.5703141467643, (53, 6616): 656.6111558452668, (53, 6617): 656.1514701951883, (53, 6618): 657.6393063181812, (53, 6619): 654.6470779795718, (53, 6620): 656.6281737670831, (53, 6621): 655.7618425494383, (53, 6622): 655.9672261714937, (53, 6623): 655.283979409338, (53, 6624): 654.5031051817202, (53, 6625): 654.3452113658171, (53, 6626): 654.6045568670704, (53, 6627): 655.1899391844893, (53, 6628): 656.4464435759304, (53, 6629): 654.735944453254, (53, 6630): 653.618825296517, (53, 6632): 654.650196096801, (53, 6634): 652.6745455314734, (53, 6635): 655.4526558343588, (53, 6636): 656.6578603135204, (53, 6637): 653.5459477959074, (53, 6638): 653.7128522415761, (53, 6639): 655.2706581414282, (53, 6640): 653.8645973215056, (53, 6641): 655.7380268777445, (53, 6642): 653.7261452518006, (53, 6643): 654.5170158067918, (53, 6645): 654.7627665414772, (53, 6646): 657.3305381726449, (53, 6647): 653.9909120870237, (53, 6653): 655.53495002379, (53, 6655): 655.2853684610595, (53, 6658): 652.6056833180323, (53, 6662): 653.6701430902928, (53, 6819): 604.1867533849627, (53, 6996): 621.7959593472401, (53, 7059): 633.395388942183, (53, 7187): 617.4621463135534, (53, 7304): 590.1296249685751, (53, 7528): 622.1794324393769, (53, 7720): 689.9072622496872, (53, 7793): 689.028362173847, (53, 7807): 689.7912037830432, (53, 7808): 688.8193872866091, (53, 7831): 661.7468217282427, (53, 7850): 672.7418165001942, (53, 7852): 670.2077963047476, (53, 8012): 685.9827939740522, (53, 8125): 699.8038665501707, (53, 8208): 711.2848877063151, (53, 8392): 670.8165279655293, (53, 8651): 548.4052519129607, (53, 9088): 600.3039466889646, (53, 9443): 526.8556840158566, (53, 9444): 528.6422426492832, (53, 9828): 481.43099871796187, (53, 9868): 474.9378352842949, (53, 10180): 701.2379169442419, (53, 10256): 731.2265195016425, (53, 10276): 716.8779324559724, (53, 10378): 719.0396713515662, (53, 10676): 694.143708679882, (53, 10714): 675.4861035681228, (53, 10730): 676.7938041558654, (53, 10862): 676.7878436009605, (53, 10881): 681.4058332531995, (53, 10883): 680.7800206692887, (53, 10885): 675.823816929683, (53, 10891): 679.8121127889127, (53, 10909): 679.6776272222555, (53, 10911): 680.604066841092, (53, 10913): 679.4482761467476, (53, 10915): 679.5440879371118, (53, 10919): 680.3074132563331, (53, 11037): 645.9479177911076, (53, 11039): 635.4320344064585, (53, 11516): 981.6971710529986, (53, 11856): 863.9223674175719, (53, 11857): 863.1577628363517, (53, 11861): 863.587994239696, (53, 11881): 861.934696304918, (53, 11902): 856.8497562742425, (53, 11911): 855.6105160194727, (53, 11914): 856.4566630750536, (53, 11922): 860.3456120398808, (53, 11924): 861.462337890256, (53, 11926): 859.9788417574836, (53, 11950): 862.5135182861667, (53, 11963): 867.3491698181307, (53, 11983): 863.466607260891, (53, 11985): 869.8056728275828, (53, 12009): 868.3299801859424, (53, 12010): 865.0353943329317, (53, 12018): 865.5268359648363, (53, 12020): 866.5352318582976, (53, 12021): 867.0431123040803, (53, 12024): 870.3171030229963, (53, 12025): 869.320828174909, (53, 12027): 868.5183540334168, (53, 12031): 864.4655222653724, (53, 12032): 865.690079275305, (53, 12035): 867.9855842746786, (53, 12041): 870.5241793692836, (53, 12045): 824.5044909425711, (53, 12145): 844.8857353770601, (53, 12275): 922.876235205485, (53, 12294): 913.2078361661985, (53, 12358): 939.459879543367, (53, 12463): 949.0574668435995, (53, 12465): 948.6914555019897, (53, 12482): 954.0808291812364, (53, 12503): 953.2458816318681, (53, 12506): 954.5215274169261, (53, 12549): 952.6606601568768, (53, 12559): 951.5087270843313, (53, 12569): 952.2355859373083, (53, 12572): 953.213229809026, (53, 12574): 951.2695234202859, (53, 12576): 953.8775086917449, (53, 12591): 954.158614901135, (53, 12608): 962.2959379841185, (53, 12696): 950.1852144798539, (53, 12710): 958.1228191302541, (53, 12728): 953.8644746202757, (53, 12766): 747.4119727162947, (53, 12771): 739.8750687180494, (53, 12790): 738.5798721917264, (53, 12795): 735.3945003543648, (53, 12797): 724.6268506135497, (53, 12798): 726.306431901672, (53, 12811): 735.5892137125054, (53, 12830): 732.1590805908737, (53, 12848): 734.4245425715484, (53, 12850): 735.596327119181, (53, 12852): 731.9095391041895, (53, 12854): 730.4788596489828, (53, 12859): 736.0174285185185, (53, 12861): 728.0335703102004, (53, 12865): 737.0632427529274, (53, 12866): 736.5155896455775, (53, 12867): 739.2127127776394, (53, 12874): 737.878000125998, (53, 12875): 739.0416638090272, (53, 12881): 734.3846880159681, (53, 12883): 736.1767656719868, (53, 12885): 739.938753373238, (53, 12888): 735.4802762957687, (53, 12889): 735.2034760582825, (53, 12892): 738.1127952770873, (53, 12893): 735.4161304405409, (53, 12896): 736.4006618035717, (53, 12906): 737.404422877318, (53, 13018): 721.3493035599018, (53, 13071): 720.8381462376782, (53, 13131): 711.9608024704096, (53, 13146): 722.0346944278098, (53, 13159): 705.4860384819963, (53, 13193): 710.3144170396326, (53, 13198): 694.7679736090721, (53, 13292): 714.2702211037733, (53, 13296): 720.976700247627, (53, 13406): 682.5244183191327, (53, 13407): 681.8372823067401, (53, 13417): 679.5068223419535, (53, 13418): 681.1482174091647, (53, 13438): 689.3191579268863, (53, 13442): 691.1344703470667, (53, 13443): 689.6749001408244, (53, 13764): 561.0436183412419, (53, 13766): 562.8932285219978, (53, 13771): 561.012389087882, (53, 13783): 559.6515785635116, (53, 13784): 564.9468071516505, (53, 13792): 557.3570291455007, (53, 13824): 558.3618551332156, (53, 14017): 570.0450553273887, (53, 14870): 682.4466247724215, (53, 14997): 609.36194221192, (53, 15000): 609.9286698982575, (53, 15003): 611.5580470970086, (53, 15006): 612.6483541532641, (53, 15007): 613.9397510142894, (53, 15056): 614.9155602496463, (53, 15063): 614.025036032968, (53, 15069): 614.0537602408057, (53, 15076): 614.4028624041385, (53, 15086): 609.9920489309974, (53, 15087): 609.1609107386931, (53, 15111): 605.0261021173949, (53, 15116): 607.4376381515486, (53, 15722): 573.9543929069303, (53, 15998): 562.5006216074512, (53, 16073): 318.50111016086214, (53, 16939): 149.8269011836494, (53, 16940): 151.6860439883544, (53, 16951): 147.32617811930697, (53, 16963): 147.69345072303, (53, 16965): 146.4148272357076, (53, 16969): 145.5530138970443, (53, 16970): 147.66449937550846, (53, 16971): 148.90457702090094, (53, 16973): 148.19646711216402, (53, 16974): 145.12178072185756, (53, 16976): 148.08707606838124, (53, 16978): 149.26729522767445, (53, 16980): 148.3458790581609, (53, 16982): 144.28524014056293, (53, 17045): 65.82894054741475, (53, 17048): 63.545527010914135, (53, 17304): 905.6878769999772, (53, 17305): 903.8136885570419, (53, 17330): 905.1875732971754, (53, 17334): 903.3976541318119, (53, 17343): 906.8605668456263, (53, 17345): 902.6392355093963, (53, 17347): 904.5812624063818, (53, 17351): 900.1330655926841, (53, 17372): 902.8768155369755, (53, 17373): 906.822088868514, (53, 17377): 907.0439025692498, (53, 17382): 904.3332340749836, (53, 17383): 905.0622243913533, (53, 17389): 903.4076405665777, (53, 17400): 906.2778038601269, (53, 17401): 906.330005714443, (53, 17402): 906.373495658987, (53, 17403): 906.5894138733529, (53, 17440): 902.0711589914293, (53, 17455): 905.940086658895, (53, 17491): 905.6957593496571, (53, 17507): 903.2874197138464, (53, 17509): 904.9900607504807, (53, 17590): 898.3576348166032, (53, 17615): 894.0119994804894, (53, 17642): 895.237890531457, (53, 17643): 894.8581453631726, (53, 17668): 894.1024335094229, (53, 17721): 891.821650331141, (53, 17754): 906.7865682799148, (53, 17769): 904.5371164096067, (53, 17776): 897.2108633195465, (53, 17804): 907.1603111458159, (53, 17809): 908.7133789466579, (53, 17824): 908.1086719156182, (53, 17837): 901.6754863562523, (53, 17838): 901.4687295385282, (53, 17862): 900.1354657685171, (53, 17866): 903.6148164651556, (53, 17872): 899.2508889704371, (53, 17873): 896.508394031261, (53, 17881): 900.6603577472232, (53, 17947): 316.0329175444992, (53, 17951): 317.71575432681783, (53, 17953): 318.75171341943746, (53, 17954): 319.09979822731253, (53, 17959): 315.1414849746751, (53, 17963): 314.51683875189286, (53, 18000): 325.7675856380806, (53, 18001): 326.234284948483, (53, 18111): 339.11587171090906, (53, 18148): 386.75267178531163, (53, 18166): 370.83069150286514, (53, 18189): 348.7304506795132, (53, 18239): 907.8639729769254, (53, 18240): 907.7607473481675, (53, 18245): 907.9650129196397, (53, 18247): 907.535511498892, (53, 18251): 907.8559215752248, (53, 18256): 908.1042150176515, (53, 18258): 907.666190694688, (53, 18259): 907.6903876224171, (53, 18260): 907.777194399555, (53, 18262): 908.0049486842821, (53, 18263): 908.1577722532309, (53, 18264): 908.2495861675588, (53, 18266): 908.0442181805439, (53, 18267): 908.1459511450898, (53, 18268): 908.1640198578431, (53, 18269): 908.3575253901333, (53, 18275): 908.2658585141621, (53, 18285): 908.2519607599146, (53, 18308): 906.1985237749542, (53, 18313): 905.2630611679323, (53, 18314): 905.4277365294128, (53, 18315): 908.5841275387753, (53, 18316): 908.4507159355553, (53, 18317): 908.5340315501187, (53, 18320): 908.7784789688308, (53, 18321): 908.7725707038961, (53, 18322): 908.9271543914195, (53, 18324): 909.2166962762681, (53, 18325): 909.8568667067606, (53, 18326): 909.6236337020406, (53, 18327): 908.5143074927332, (53, 18329): 910.2723381978348, (53, 18330): 909.5955380744055, (53, 18331): 909.2236265358716, (53, 18332): 908.7812592610031, (53, 18333): 909.6309072012159, (53, 18336): 909.4430557863536, (53, 18337): 909.7336113064617, (53, 18403): 908.7642993294206, (53, 18432): 896.6574383860268, (53, 18451): 904.8513537542955, (53, 18466): 913.1104339720773, (53, 18481): 909.0524289501726, (53, 18483): 908.9722344647053, (53, 18484): 908.6811205707861, (53, 18485): 907.8844809468815, (53, 18486): 909.1116540349601, (53, 18487): 908.3867467820396, (53, 18489): 908.7455309228349, (53, 18490): 909.7784482048176, (53, 18491): 910.1647005643214, (53, 18492): 907.4955009016869, (53, 18493): 909.0681755412432, (53, 18494): 908.524523575742, (53, 18495): 909.5024446450108, (53, 18496): 909.0328885461215, (53, 18497): 908.2922470418802, (53, 18498): 908.1609369081566, (53, 18499): 908.7328424191811, (53, 18501): 908.4579154914619, (53, 18502): 908.1008816345341, (53, 18503): 907.7313306608331, (53, 18504): 909.0954502668156, (53, 18506): 908.7378801688118, (53, 18507): 908.4416342529734, (53, 18508): 908.7295686849078, (53, 18509): 908.8114530253556, (53, 18510): 907.8503040201593, (53, 18511): 909.3384933639843, (53, 18512): 908.7567070884824, (53, 18515): 909.2420720140285, (53, 18516): 909.5289822029729, (53, 18517): 909.1897062124959, (53, 18518): 909.7631697304224, (53, 18519): 909.1292800410022, (53, 18520): 908.52716052085, (53, 18522): 910.5388339368299, (53, 18523): 910.7065626117222, (53, 18532): 911.3477653244071, (53, 18535): 910.1039817664661, (53, 18537): 909.4115121805655, (53, 18539): 909.6011329966508, (53, 18540): 909.7290816125831, (53, 18541): 910.1090226217706, (53, 18542): 910.3420855936532, (53, 18543): 909.2192623885176, (53, 18546): 909.8977291877047, (53, 18555): 910.9910741648044, (53, 18556): 911.247979010948, (53, 18565): 911.3822341551219, (53, 18567): 911.8686317361281, (53, 18568): 911.2011489816484, (53, 18577): 915.4411034225093, (53, 18583): 914.4961175450645, (53, 18605): 915.1062589173087, (53, 18608): 912.5717430059802, (53, 18616): 919.082668989638, (53, 18618): 922.6145222094453, (53, 18625): 920.8380281446414, (53, 18645): 917.5945076393864, (53, 18646): 918.5793522481815, (53, 18653): 916.3526080868903, (53, 18654): 919.0973782462536, (53, 18655): 917.4202534969379, (53, 18666): 927.3634122105516, (53, 18837): 905.7411209600808, (53, 18974): 902.7775310466169, (53, 18999): 904.53249593035, (53, 19000): 905.5293034223814, (53, 19174): 852.7125869690365, (53, 19342): 871.2572963548788, (53, 19455): 864.0380013018693, (53, 19555): 812.790796080679, (53, 19564): 814.0077785160752, (53, 19573): 812.2613714059866, (53, 19586): 811.5928749062663, (53, 19605): 812.6567347090712, (53, 19611): 813.9032599803708, (53, 19614): 813.8009953208696, (53, 19641): 836.7416331841183, (53, 19702): 835.8024365807245, (53, 19713): 834.234202466373, (53, 19731): 807.1773238681562, (53, 19819): 855.4127782452127, (53, 19893): 817.759000586548, (53, 19899): 828.8069764651358, (53, 19929): 820.6874470010843, (53, 19951): 842.7820798279593, (53, 19962): 822.4435591302406, (53, 19970): 827.4034864324898, (53, 19971): 827.4836210324282, (53, 19972): 825.6031062069068, (53, 19975): 824.7415008689105, (53, 19978): 847.6375222487104, (53, 19987): 848.0460013137133, (53, 19989): 841.948348003254, (53, 20039): 849.1812040874637, (53, 20043): 851.7695446700469, (53, 20047): 849.8525903509923, (53, 20052): 843.0718780015786, (53, 20054): 843.5862060506068, (53, 20085): 874.4812741387954, (53, 20104): 876.4056812764867, (53, 20132): 864.5789089586963, (53, 20203): 816.216507726901, (53, 20280): 813.5562447859157, (53, 20285): 812.8486212256853, (53, 20290): 814.656501676346, (53, 20297): 812.6025284314876, (53, 20309): 848.8392260595481, (53, 20453): 880.9739639558021, (53, 20485): 799.6526351494197, (53, 20520): 794.4433712385882, (53, 20526): 792.3125490538392, (53, 20698): 510.0084187341705, (53, 20868): 447.08340095459687, (53, 21042): 743.1283591431246, (53, 21057): 755.8062299818656, (53, 21066): 749.901462895844, (53, 21075): 747.0694816520243, (53, 21093): 744.5158606031999, (53, 21098): 754.1507413607872, (53, 21127): 744.4024993596546, (53, 21130): 747.0080446354173, (53, 21144): 746.2399325562399, (53, 21146): 743.5712372631659, (53, 21147): 745.9053858496878, (53, 21148): 748.2524102243772, (53, 21153): 741.3972340175748, (53, 21293): 764.7146015887957, (53, 21426): 757.501409458984, (53, 21442): 770.2525231170384, (53, 21451): 771.5007780424095, (53, 21466): 764.0606411997915, (53, 21469): 766.1514625977903, (53, 21471): 762.9913626789101, (53, 21473): 764.769734243064, (53, 21475): 763.2342423734418, (53, 21482): 767.3052486771941, (53, 21484): 766.9579556274274, (53, 21488): 765.6865518945218, (53, 21494): 763.4529725280432, (53, 21498): 764.9520512398844, (53, 21500): 762.761987396213, (53, 21514): 767.7168628006057, (53, 21537): 762.8393635697665, (53, 21662): 770.1399731179685, (53, 21691): 762.1376451854599, (53, 21757): 746.160685278396, (53, 21777): 719.9451271700971, (53, 21778): 717.9314604245442, (53, 21779): 719.2489289801297, (53, 21790): 722.003873256669, (53, 21802): 722.2741630798048, (53, 21824): 724.5571608232557, (53, 21874): 720.0072297920535, (53, 21879): 719.1725141760868, (53, 21983): 725.7189658875425, (53, 22002): 748.7293095804148, (53, 22132): 730.5192549661308, (53, 22261): 485.93715840874887, (53, 22298): 491.5758734322907, (53, 22339): 477.532429127423, (53, 22508): 519.9984096854027, (53, 22841): 189.27021553350195, (53, 22842): 188.19703820601677, (53, 22874): 184.80950970257186, (53, 22941): 188.4113836920179, (53, 22956): 187.31274855270047, (53, 22960): 189.84266291973157, (53, 22968): 175.0124651022853, (53, 22970): 177.10075224849825, (53, 22974): 167.7455854198328, (53, 22980): 167.52702083004593, (53, 23025): 154.09098964994467, (53, 23028): 151.3649494829433, (53, 23081): 134.20675956630933, (53, 23104): 111.6221148044681, (53, 23147): 155.82901536565095, (53, 23298): 803.8945175582173, (53, 23376): 798.2076580522548, (53, 23381): 795.8160566273943, (53, 23529): 808.3558404611493, (53, 23556): 804.9367771906748, (53, 23718): 799.5480561077447, (53, 24001): 837.3507275799528, (53, 24094): 849.6700359602884, (53, 24129): 855.3227420993085, (53, 24174): 844.3013958066502, (53, 24235): 857.3414443563481, (53, 24259): 862.2684295343877, (53, 24260): 861.936384958019, (53, 24261): 860.6539849603614, (53, 24305): 868.519334428112, (53, 24306): 869.7108428419275, (53, 24307): 868.006060979528, (53, 24308): 850.1364610823713, (53, 24498): 881.2724908061524, (53, 24499): 881.4334079437627, (53, 24500): 880.3483503038941, (53, 24668): 871.2357786513553, (53, 24711): 889.2297652361975, (53, 24756): 893.8072715767051, (53, 24788): 895.0974402321533, (53, 24809): 889.599984597458, (53, 24813): 891.2452208209472, (53, 24821): 890.6715435907676, (53, 24825): 891.2410145400703, (53, 24832): 889.1121692369926, (53, 24833): 890.0344271933192, (53, 24835): 890.9969534692729, (53, 24837): 892.3608050793927, (53, 24840): 889.0225339804979, (53, 24841): 890.337311640827, (53, 24844): 889.1365926428309, (53, 24845): 889.6947450551908, (53, 24846): 890.0116935907241, (53, 24849): 890.5490100436568, (53, 24850): 891.6151388329001, (53, 24863): 878.2676110655533, (53, 24866): 879.8891473659818, (53, 24885): 882.0840012574623, (53, 24886): 882.3837510940311, (53, 24889): 885.4233820211716, (53, 24903): 886.565416158328, (53, 24909): 880.178636645701, (53, 24999): 948.9019484169872, (53, 25019): 946.3149443358061, (53, 25028): 948.1035115037924, (53, 25137): 817.1876292345027, (53, 25145): 819.4378468195584, (53, 25208): 844.8490753758648, (53, 25233): 841.7793522789768, (53, 25371): 817.5543851588831, (53, 25377): 811.1977434194831, (53, 25828): 696.298457008517, (53, 25851): 678.5677623754939, (53, 25874): 695.2287751061367, (53, 25898): 703.0110463611898, (53, 25946): 694.4984117746843, (53, 26047): 731.5070510200056, (53, 26066): 771.2788577554737, (53, 26197): 745.4549701639905, (53, 26212): 642.007575219355, (53, 26253): 636.6343892829311, (53, 26254): 638.5424308648459, (53, 26257): 640.8670351612458, (53, 26258): 637.8430488727051, (53, 26260): 639.3643704971, (53, 26266): 636.2917479739133, (53, 26267): 638.2534313573733, (53, 26271): 638.4413129470998, (53, 26304): 657.0641488266577, (53, 26305): 656.5858529569076, (53, 26363): 691.0806542803412, (53, 26441): 520.4586353334461, (53, 26442): 520.1694435488596, (53, 26450): 522.607244091111, (53, 26459): 525.9374986367661, (53, 26462): 527.0010591390281, (53, 26467): 520.5345811064034, (53, 26471): 520.7178302880575, (53, 26472): 520.43762535957, (53, 26473): 520.055962459255, (53, 26476): 516.4406413648506, (53, 26485): 523.2534819365807, (53, 26493): 521.5641501160607, (53, 26524): 527.4459163928034, (53, 26525): 526.8291148148506, (53, 26556): 521.7501989088705, (53, 26560): 524.6369949198897, (53, 26561): 526.6513505124993, (53, 26564): 521.6243271415437, (53, 26569): 526.1104715552699, (53, 26570): 525.6538571275378, (53, 26573): 523.8783974429672, (53, 26581): 522.6722535087822, (53, 26583): 523.9403419252578, (53, 26593): 521.0698361923647, (53, 26837): 518.7935201252042, (53, 26844): 517.9252664285588, (53, 26863): 516.7289332166978, (53, 26893): 512.8775917140292, (53, 26902): 511.5728430077069, (53, 26905): 515.7015941521145, (53, 26912): 513.8002473612025, (53, 26921): 515.0706681145225, (53, 26922): 513.4204573490158, (53, 27212): 580.5943107593707, (53, 27218): 584.5873332048791, (53, 27239): 578.4769727795879, (53, 27257): 578.1498429669592, (53, 27274): 577.5650782469993, (53, 27279): 576.5234299487388, (53, 27282): 577.4607555456737, (53, 27283): 579.4138281593457, (53, 27285): 576.4266850777228, (53, 27286): 575.1900082428949, (53, 27290): 578.0727845059563, (53, 27295): 580.4296758319014, (53, 27300): 577.8797990714465, (53, 27344): 575.0258879457292, (53, 27366): 572.7725433177167, (53, 27383): 573.8279470997771, (53, 27398): 575.637937470732, (53, 27406): 577.4273330616347, (53, 27407): 578.1231342279111, (53, 27426): 587.4696315527858, (53, 27432): 588.8862332659461, (53, 27460): 589.074356139007, (53, 27523): 554.0270465386843, (53, 27545): 559.227754570752, (53, 27602): 532.4163392207583, (53, 27606): 533.7547397230483, (53, 27646): 530.4243279980371, (53, 27667): 525.0041538135396, (53, 27672): 525.674682062605, (53, 27674): 525.9966391692309, (53, 27688): 528.9850151973156, (53, 27692): 523.6617525838889, (53, 27693): 524.2631151540149, (53, 27705): 523.2242090175461, (53, 27712): 522.012935366095, (53, 27786): 572.9534492188568, (53, 27790): 588.7586065856992, (53, 27791): 590.9368701515524, (53, 27795): 572.5585538723935, (53, 27801): 583.0398675770484, (53, 27813): 570.8674320336972, (53, 27816): 574.2455318890169, (53, 27823): 583.5627943040032, (53, 27830): 578.1620143523477, (53, 27884): 529.2631489552622, (53, 27885): 531.0920476696294, (53, 27896): 530.4529743315672, (53, 27919): 531.4029069632505, (53, 27922): 530.1453509277112, (53, 27930): 530.7695263288996, (53, 27934): 529.9459222536681, (53, 27935): 528.9783732612779, (53, 27948): 482.66394912455576, (53, 27951): 498.2338856052852, (53, 28061): 407.6850945625185, (53, 28290): 354.85405126976286, (53, 28292): 349.4988490824771, (53, 28293): 353.4625448648672, (53, 28295): 351.12643228816967, (53, 28296): 353.4237556821956, (53, 28297): 357.3935070622007, (53, 28302): 355.24913179168277, (53, 28310): 212.736463924354, (53, 28313): 212.21824182842366, (53, 28372): 209.59441055113936, (53, 28398): 209.54453914163835, (53, 28399): 210.44576687739237, (53, 28400): 209.2390603888389, (53, 28401): 212.17581004321872, (53, 28445): 214.2243251434251, (53, 28475): 213.6301230628946, (53, 28885): 858.4592867664885, (53, 28886): 857.3985981430169, (53, 28915): 858.417979728578, (53, 28916): 857.4753687335032, (53, 28917): 856.9060285497898, (53, 28921): 860.454543760899, (53, 28931): 860.185361043374, (53, 28945): 855.0836340668515, (53, 28982): 856.3162839499632, (53, 29219): 862.7964885032478, (53, 29228): 857.9151228495042, (53, 29246): 889.6294791063643, (53, 29248): 889.1981965217489, (53, 29282): 882.6229083153795, (53, 29290): 892.8352266152551, (53, 29291): 891.5225643327713, (53, 29292): 892.7546146259791, (53, 29293): 890.1832378429486, (53, 29294): 892.2362197815154, (53, 29298): 890.382802727788, (53, 29299): 890.1672379659046, (53, 29304): 887.7539654711943, (53, 29317): 881.5728785956829, (53, 29323): 881.0919266543395, (53, 29330): 884.0716926126504, (53, 29331): 885.5458717010345, (53, 29344): 863.4143581815765, (53, 29445): 807.5680238778614, (53, 29724): 232.94113912894807, (53, 29738): 232.80162408516873, (53, 29745): 234.83468907449227, (53, 29748): 242.9403014641564, (53, 29750): 246.1728225281729, (53, 29759): 242.12572074691082, (53, 29772): 241.76291709025617, (53, 29781): 242.07332818593125, (53, 29784): 238.61994150368645, (53, 29790): 243.44157394191365, (53, 29811): 247.26407886568762, (53, 29817): 268.0492213852374, (53, 29818): 268.4581689736189, (53, 29929): 229.77540829463857, (53, 30039): 205.02704867663516, (53, 30066): 192.90161426102648, (53, 30116): 218.12097757887352, (53, 30238): 258.15101429905496, (53, 30248): 216.46092027725462, (53, 30260): 214.10591296854244, (53, 30545): 841.2268416054792, (53, 30733): 788.2096220121476, (53, 30756): 775.9399764364529, (53, 30921): 800.6803228075979, (53, 31079): 653.4736507576043, (53, 31149): 649.9212431468123, (53, 31154): 649.512887448296, (53, 31160): 649.6051428488285, (53, 31163): 648.7244186832503, (53, 31189): 629.1713931028829, (53, 31215): 629.8042202154957, (53, 31259): 624.7444012462864, (53, 31262): 622.7737823274066, (53, 31430): 653.9595485042399, (53, 31568): 591.9272437412217, (53, 31751): 641.078414918523, (55, 109): 735.3529803448896, (55, 872): 394.57012885225066, (55, 873): 393.7581213439973, (55, 877): 392.81823699257524, (55, 879): 392.5766214092143, (55, 884): 390.623959845513, (55, 889): 390.6956787519976, (55, 891): 391.23170455567526, (55, 892): 392.20840707987134, (55, 894): 392.81984809738134, (55, 896): 395.662762881157, (55, 903): 391.36811713237364, (55, 909): 396.8355766009216, (55, 910): 397.65742117953494, (55, 912): 397.92846832762535, (55, 913): 397.81201251524277, (55, 916): 399.43982562299, (55, 926): 398.9049776085882, (55, 927): 399.4333199891333, (55, 948): 391.7339217648767, (55, 961): 396.23968213423314, (55, 962): 396.95098185078587, (55, 963): 397.4920622671319, (55, 967): 391.5293091950287, (55, 974): 389.06571189040176, (55, 998): 390.1853800123682, (55, 1014): 391.22342684425996, (55, 1086): 429.9953947765209, (55, 1087): 434.20601741864556, (55, 1089): 432.6798454646596, (55, 1090): 432.05188846978143, (55, 1092): 431.06143314587706, (55, 1097): 431.00193478220496, (55, 1107): 433.1958126796844, (55, 1387): 623.7638437339593, (55, 1554): 639.0179326011615, (55, 1827): 341.6987160170105, (55, 1828): 342.2882637662488, (55, 1829): 341.82980415455063, (55, 1830): 338.97319791608817, (55, 1831): 339.466158870946, (55, 1832): 339.77389000874496, (55, 1833): 340.2678846803623, (55, 1836): 340.85725174502903, (55, 1841): 339.9627689585732, (55, 1843): 340.0307805494719, (55, 1844): 339.50717554711235, (55, 1845): 339.15580884220486, (55, 1847): 340.8891153319687, (55, 1848): 340.61317485950707, (55, 1849): 338.85396739064794, (55, 1850): 339.1827761819795, (55, 1851): 339.0827356384038, (55, 1852): 337.92150944661734, (55, 1854): 338.6962340364538, (55, 1856): 339.4125201052229, (55, 1857): 340.00636408849334, (55, 1858): 339.7697752628806, (55, 1861): 340.8577413312519, (55, 1866): 338.4395702918395, (55, 1867): 340.9259462870162, (55, 1868): 341.91821290244525, (55, 1870): 338.0376420994825, (55, 1871): 341.90393812617924, (55, 1875): 339.48227874491926, (55, 1880): 340.28277874764814, (55, 1882): 338.577763188587, (55, 1883): 340.4801318929675, (55, 1889): 342.0856926993184, (55, 1893): 343.6958424153995, (55, 1894): 344.1187838529833, (55, 1899): 342.95855784416796, (55, 1900): 343.2765927189093, (55, 1902): 343.5319159354895, (55, 1905): 342.66078691938384, (55, 1907): 341.66770114925725, (55, 1910): 343.03767605248134, (55, 1917): 346.166316502186, (55, 1920): 342.6685252835425, (55, 1935): 344.852792967107, (55, 1937): 344.3765436439412, (55, 1946): 345.76826781956777, (55, 1949): 346.269432584248, (55, 1950): 343.67513756809745, (55, 1951): 344.29270295356054, (55, 1952): 341.2327689155502, (55, 1953): 343.926217236759, (55, 1954): 341.984319600936, (55, 1958): 345.05448342355754, (55, 1960): 344.192405141264, (55, 1968): 343.8601291871628, (55, 1969): 347.06260586325453, (55, 1974): 346.0199022779314, (55, 1975): 345.27329278909866, (55, 1979): 346.80203791518676, (55, 1980): 344.57619091954643, (55, 1981): 345.96256561949633, (55, 1985): 346.5702316430172, (55, 1994): 338.63925579561453, (55, 2011): 337.8202269719783, (55, 2019): 334.3373491208569, (55, 2020): 334.77494287989026, (55, 2029): 334.2844373616437, (55, 2030): 335.11431231185327, (55, 2032): 333.0863390904207, (55, 2033): 334.4362743258709, (55, 2034): 333.3377014551825, (55, 2036): 328.7009353029997, (55, 2037): 330.0586324357826, (55, 2038): 335.202973608997, (55, 2042): 333.67939702047545, (55, 2050): 336.10384174822167, (55, 2051): 334.94383991419187, (55, 2053): 335.42087000415313, (55, 2054): 335.2401892858082, (55, 2066): 335.4017605799555, (55, 2067): 336.00640638341986, (55, 2071): 339.50934300001484, (55, 2072): 340.155368514917, (55, 2073): 343.78800799210137, (55, 2074): 343.0726753817019, (55, 2080): 341.581581303819, (55, 2082): 340.24318048272664, (55, 2083): 340.65384166776005, (55, 2089): 341.66388904821713, (55, 2090): 342.24513659364646, (55, 2092): 342.9973350133264, (55, 2098): 342.9456639422259, (55, 2099): 342.1489635280046, (55, 2101): 341.94074024418893, (55, 2102): 342.83976177157393, (55, 2103): 342.13281749061787, (55, 2104): 341.2630265774426, (55, 2106): 340.1498822480442, (55, 2112): 341.09970088983096, (55, 2113): 342.3379834087396, (55, 2114): 340.7792326617254, (55, 2117): 339.3762932561314, (55, 2123): 379.31757845701253, (55, 2124): 379.5320452520994, (55, 2134): 376.19560592751105, (55, 2138): 377.9102215765947, (55, 2141): 377.1080882638565, (55, 2148): 366.81861597061555, (55, 2150): 376.10090907812656, (55, 2151): 375.53898150469234, (55, 2152): 375.2689284012999, (55, 2153): 367.8978697736979, (55, 2154): 367.72963705388077, (55, 2155): 365.8492244012834, (55, 2156): 366.9789281683875, (55, 2157): 360.66144264431125, (55, 2160): 373.10040932675304, (55, 2161): 374.1850767106886, (55, 2162): 363.91482882001446, (55, 2163): 363.98886556090184, (55, 2164): 363.326528069637, (55, 2168): 370.75578140043575, (55, 2172): 366.0893040782281, (55, 2174): 374.1828772834838, (55, 2178): 364.8273504466641, (55, 2179): 364.29907621577416, (55, 2183): 376.66878669211326, (55, 2185): 376.0268042295259, (55, 2186): 376.20529441898736, (55, 2190): 374.3020532292965, (55, 2192): 374.3949879133453, (55, 2193): 377.09507240477393, (55, 2194): 377.18701031901855, (55, 2195): 375.79600378489846, (55, 2197): 373.68703087911825, (55, 2205): 371.8358854717922, (55, 2207): 369.8863739086806, (55, 2208): 370.6947058186288, (55, 2212): 380.1514472140013, (55, 2214): 357.88064700072675, (55, 2225): 353.8775776897692, (55, 2231): 383.385545721401, (55, 2278): 344.60324301032546, (55, 2284): 342.28438735731555, (55, 2285): 341.3676486644914, (55, 2291): 335.38119859273166, (55, 2292): 342.74011256662897, (55, 2307): 342.135458395021, (55, 2313): 333.1044517506779, (55, 2317): 345.79223829895017, (55, 2319): 341.9815032698549, (55, 2321): 340.72011704532645, (55, 2323): 342.8062811403248, (55, 2326): 346.5620191576273, (55, 2327): 346.5946763351889, (55, 2329): 346.4039451305285, (55, 2330): 345.69748865935526, (55, 2332): 344.6566549020226, (55, 2344): 347.75401899273123, (55, 2346): 346.30188364337795, (55, 2361): 358.465750306139, (55, 2368): 351.23915416580047, (55, 2374): 350.10547433083286, (55, 2375): 350.83658772575774, (55, 2377): 351.97396636832656, (55, 2378): 350.2026619208452, (55, 2379): 348.7259513718893, (55, 2380): 349.76561490157223, (55, 2383): 352.8392968307151, (55, 2385): 353.3364499612226, (55, 2395): 354.64052377562473, (55, 2397): 348.07087573865743, (55, 2398): 352.1842929689135, (55, 2399): 352.790882814935, (55, 2400): 352.8373694181961, (55, 2402): 348.61482321442577, (55, 2403): 348.4679768530886, (55, 2404): 349.0339105080476, (55, 2405): 348.84777894730087, (55, 2407): 349.8725519474068, (55, 2408): 349.07881594872947, (55, 2409): 349.1324537454463, (55, 2411): 346.02067290665985, (55, 2412): 346.97708191581074, (55, 2413): 346.52181191516036, (55, 2414): 346.38339254939757, (55, 2422): 345.21086048163403, (55, 2424): 347.4732859049882, (55, 2426): 347.94059339770615, (55, 2433): 347.234960656707, (55, 2436): 345.7000366989037, (55, 2437): 346.9822830442474, (55, 2440): 347.12801339056045, (55, 2445): 331.0437298732489, (55, 2447): 332.68823098651313, (55, 2454): 332.5037072463039, (55, 2455): 333.67660958927223, (55, 2460): 332.752582527427, (55, 2461): 332.5948014811943, (55, 2471): 325.16123853595917, (55, 2492): 280.02604093225017, (55, 2511): 288.40234342913544, (55, 2523): 283.92227571309155, (55, 2525): 281.541975779902, (55, 2535): 305.68561081439395, (55, 2537): 305.04791742719584, (55, 2538): 306.6623237426085, (55, 2539): 300.8824414147199, (55, 2540): 305.83168876582863, (55, 2542): 304.2750159010404, (55, 2559): 318.6711443071564, (55, 2575): 311.3441464682568, (55, 2599): 325.43412240903814, (55, 2600): 321.57388546662304, (55, 2607): 328.2281912003286, (55, 2627): 267.5331992825851, (55, 2647): 263.3568013033854, (55, 2674): 269.73980540456074, (55, 2681): 266.7297794063813, (55, 2683): 267.99499071784555, (55, 2686): 269.5940623731484, (55, 2689): 267.48578914884644, (55, 2690): 266.760564060873, (55, 2713): 245.43160391385476, (55, 2714): 242.52404303588116, (55, 2715): 242.7793894423876, (55, 2739): 243.42997698794412, (55, 2740): 250.21267350118913, (55, 2741): 250.9168038642483, (55, 2749): 239.95432083549673, (55, 2750): 241.08529178699297, (55, 2752): 241.74104935781483, (55, 2755): 241.27014230296496, (55, 2758): 240.325962679199, (55, 2759): 240.80093052363534, (55, 2769): 241.72037772592455, (55, 2771): 248.4135246052066, (55, 2779): 240.78240599470263, (55, 2784): 235.2347379678197, (55, 2800): 228.02835651411888, (55, 2802): 245.6918237617892, (55, 2803): 246.57986571918747, (55, 2804): 246.83051232159113, (55, 2805): 242.9515644134721, (55, 2807): 243.9142492694853, (55, 2809): 241.66428641678004, (55, 2812): 242.93507450330276, (55, 2814): 235.15928163512407, (55, 2817): 226.53065827373996, (55, 2819): 246.3282140536952, (55, 2823): 234.63127910361482, (55, 2832): 241.82032584038276, (55, 2836): 241.0895095782677, (55, 2839): 244.90072773918558, (55, 2841): 230.9637466007506, (55, 2843): 232.45731781288362, (55, 2846): 237.3024404712258, (55, 2849): 240.2988829153691, (55, 2852): 240.74685669550885, (55, 2853): 240.03400778337235, (55, 2876): 235.58878414952227, (55, 2877): 235.57962245807792, (55, 2885): 226.61462988000343, (55, 2918): 252.65840023075674, (55, 2921): 251.74434751862455, (55, 2925): 259.2570436220316, (55, 2926): 263.614839272569, (55, 2930): 248.78746388004333, (55, 2931): 256.65689923607056, (55, 2938): 250.96412613014843, (55, 2940): 259.6844657361895, (55, 2947): 260.99259947076496, (55, 2949): 252.62096725770715, (55, 2950): 251.05202739767316, (55, 2952): 250.8949779459089, (55, 2958): 251.56163467967266, (55, 2959): 253.598576603082, (55, 2960): 253.19629036370847, (55, 2961): 252.31294139483467, (55, 2963): 250.5046379077922, (55, 2968): 249.57960323611658, (55, 2976): 251.49034242313112, (55, 2981): 237.6073652577563, (55, 2982): 235.57182561829936, (55, 2984): 235.0203160366195, (55, 3003): 232.66385408071343, (55, 3046): 254.25301139956036, (55, 3050): 244.3148678574132, (55, 3051): 245.13986485267807, (55, 3053): 244.11461364651302, (55, 3069): 242.0171853350363, (55, 3071): 248.60249810433302, (55, 3080): 223.32866831940788, (55, 3199): 220.29876072592828, (55, 3200): 218.71792877838044, (55, 3205): 221.5723144993801, (55, 3209): 218.62576124449822, (55, 3215): 219.82027790817182, (55, 3217): 219.22261888632966, (55, 3249): 221.0188364914651, (55, 3263): 226.5646954662044, (55, 3289): 225.59435545895224, (55, 3301): 222.92162795993025, (55, 3302): 223.7294095463347, (55, 3307): 223.74103333225352, (55, 3310): 223.2005728631751, (55, 3391): 169.97954975290477, (55, 3509): 362.63246779326795, (55, 3510): 363.64210453561475, (55, 3511): 363.73769033596835, (55, 3512): 365.0339735488922, (55, 3514): 365.435401280284, (55, 3519): 356.52295109352013, (55, 3536): 362.22474338278175, (55, 3545): 361.45763027227935, (55, 3548): 364.0038263048768, (55, 3572): 360.7127206697942, (55, 3581): 359.3679988755439, (55, 3583): 363.2130722074991, (55, 3601): 353.4325598161275, (55, 3656): 352.22974895125907, (55, 3669): 348.31036645205853, (55, 3670): 347.10168521200285, (55, 3695): 355.0278729158656, (55, 3696): 354.37200007805797, (55, 3782): 377.7756271215837, (55, 3792): 376.59035458017274, (55, 3989): 856.3373878381352, (55, 4008): 861.8679643223654, (55, 4031): 858.9097919368013, (55, 4045): 859.42205026009, (55, 4144): 862.1497798603953, (55, 4145): 859.2028891972573, (55, 4164): 860.6277843413694, (55, 4168): 860.1231691879191, (55, 4173): 860.379734465, (55, 4181): 856.9859879689698, (55, 4228): 851.030966427091, (55, 4248): 853.3598682653909, (55, 4254): 834.1010746642661, (55, 4260): 833.0583631932071, (55, 4262): 835.7627630180768, (55, 4273): 834.5955696139084, (55, 4319): 822.0368500980145, (55, 4326): 821.1810135459795, (55, 4328): 821.1152891217386, (55, 4334): 823.1137418814337, (55, 4335): 822.8790786674084, (55, 4372): 868.1686296418026, (55, 4413): 892.5664528781109, (55, 4434): 866.9766885043803, (55, 4447): 869.4900611591619, (55, 4452): 867.4034201019183, (55, 4463): 822.4873623849131, (55, 4465): 823.9203259399512, (55, 4619): 896.8621017764968, (55, 4645): 901.70603265279, (55, 4657): 901.0811407416468, (55, 4666): 899.2646798085251, (55, 4676): 902.7992110903948, (55, 4678): 903.5080468808407, (55, 4689): 901.2971446332165, (55, 4704): 918.8735990566144, (55, 4726): 963.7473039617095, (55, 4727): 962.9350197825719, (55, 4730): 961.3571890470573, (55, 4731): 961.8231707028478, (55, 4734): 962.6303945423934, (55, 4735): 961.873093932548, (55, 4736): 962.2730801491531, (55, 4737): 960.9209675835559, (55, 4738): 961.1122245329697, (55, 4756): 961.9315224646855, (55, 4760): 957.7863934533262, (55, 4761): 958.2194633911458, (55, 4762): 956.6893399810801, (55, 4765): 958.1953760382827, (55, 4773): 965.3363694485547, (55, 4774): 964.6082352889023, (55, 4790): 964.7971732788197, (55, 4795): 964.0883217953203, (55, 4799): 964.9568953510409, (55, 4801): 966.6482756473179, (55, 4804): 964.3668851257532, (55, 4805): 963.7837550092576, (55, 4806): 964.2930770470915, (55, 4815): 963.5104554311033, (55, 4816): 965.5456053355816, (55, 4817): 965.9392515133633, (55, 4826): 964.7320622852808, (55, 4830): 963.5763637735876, (55, 4839): 960.1576054222058, (55, 4840): 960.8854224093101, (55, 4841): 959.1727888423416, (55, 4846): 958.6081015795244, (55, 4848): 958.4269889360477, (55, 4850): 959.1665225074122, (55, 4871): 949.6847073186532, (55, 4883): 956.8600122226195, (55, 4900): 953.1576325365545, (55, 4901): 952.1517814639915, (55, 4917): 896.8298039541609, (55, 4931): 890.8827791557878, (55, 4944): 897.5049754252093, (55, 4956): 891.9726338083127, (55, 4958): 891.7975574248642, (55, 4959): 890.6661008734064, (55, 4961): 893.177659276464, (55, 4966): 890.5179377075831, (55, 5207): 883.9284794637139, (55, 5272): 766.5702580010163, (55, 5283): 768.8499925838197, (55, 5287): 772.7864504399797, (55, 5289): 773.7933608812149, (55, 5293): 766.6682698477175, (55, 5295): 773.0091106334347, (55, 5296): 773.1558360854538, (55, 5298): 773.1862647661782, (55, 5303): 775.2106897868673, (55, 5305): 765.6391534547641, (55, 5306): 764.1536186367458, (55, 5307): 764.4830842490258, (55, 5308): 766.7400963383527, (55, 5313): 766.4018375467011, (55, 5314): 767.7547428652754, (55, 5317): 766.8774855906294, (55, 5319): 773.0810170840854, (55, 5324): 771.6629731364845, (55, 5326): 770.7368713378511, (55, 5348): 763.7923418068693, (55, 5351): 765.7168669763557, (55, 5399): 775.3264477233033, (55, 5413): 768.9687868768798, (55, 5422): 776.3676980146344, (55, 5445): 771.3039096712529, (55, 5448): 769.1627786965487, (55, 5456): 768.8532379986631, (55, 5467): 770.8914846485654, (55, 5624): 746.6230602544704, (55, 5671): 813.903334431895, (55, 5672): 810.9200725356208, (55, 5797): 849.1111702823132, (55, 5871): 806.5673212387886, (55, 5976): 781.6928393306109, (55, 6118): 184.39076670346307, (55, 6248): 140.87500843742893, (55, 6345): 604.9867103212488, (55, 6352): 597.9404705750248, (55, 6354): 606.9826880208325, (55, 6359): 607.8898310264478, (55, 6376): 597.874838880351, (55, 6378): 606.0913821970544, (55, 6381): 606.9769825614853, (55, 6383): 603.6864508563366, (55, 6396): 604.2872189414761, (55, 6399): 604.4915344467089, (55, 6408): 598.6839647889778, (55, 6409): 603.3006317766303, (55, 6419): 594.0408909124167, (55, 6422): 600.6334051862057, (55, 6423): 600.1386449774038, (55, 6424): 607.756335852713, (55, 6439): 606.8331230066088, (55, 6464): 605.3015788100843, (55, 6465): 604.1431849843295, (55, 6469): 604.0636123771193, (55, 6470): 603.4134417436325, (55, 6472): 610.0896645788916, (55, 6480): 610.7927117456871, (55, 6486): 617.352750385333, (55, 6497): 615.2604233962745, (55, 6503): 608.5262537508638, (55, 6508): 607.5128909746494, (55, 6509): 609.554343838384, (55, 6521): 612.6710260440764, (55, 6544): 613.6177405895327, (55, 6552): 604.2354168425168, (55, 6553): 603.2960732121542, (55, 6554): 602.3214321937963, (55, 6578): 605.5977197928142, (55, 6582): 606.3760251418317, (55, 6601): 606.3484089210154, (55, 6609): 612.7238615667045, (55, 6610): 613.3171616734762, (55, 6611): 612.7148759446601, (55, 6614): 611.7202921524594, (55, 6615): 612.181265637068, (55, 6616): 614.2629243353052, (55, 6617): 613.4381133801681, (55, 6618): 615.9739197638754, (55, 6619): 611.1516920761496, (55, 6620): 614.7858555320552, (55, 6621): 614.0362045008891, (55, 6622): 613.887450591831, (55, 6623): 612.1671279967487, (55, 6624): 611.9272178040549, (55, 6625): 611.4983114576822, (55, 6626): 610.8888373439851, (55, 6627): 611.081234055552, (55, 6628): 615.1231713316071, (55, 6629): 612.779391867633, (55, 6630): 609.9698195298874, (55, 6632): 612.413210734943, (55, 6634): 609.3623344696663, (55, 6635): 613.4576273737057, (55, 6636): 614.4842377093411, (55, 6637): 611.6635670235199, (55, 6638): 610.5446371820517, (55, 6639): 611.4556761282489, (55, 6640): 610.438259788924, (55, 6641): 614.4100143445565, (55, 6642): 610.89524438824, (55, 6643): 610.4423632368472, (55, 6645): 611.495853294851, (55, 6646): 615.2711766236115, (55, 6647): 610.9689900362902, (55, 6653): 611.9906981269316, (55, 6655): 611.3061478145539, (55, 6658): 609.4926118987873, (55, 6662): 611.2027413094713, (55, 6819): 569.9200268163287, (55, 6996): 594.8083992334645, (55, 7059): 605.5778922478902, (55, 7187): 608.5479303029239, (55, 7304): 573.1624637302812, (55, 7528): 602.8012152036802, (55, 7720): 660.0443690835478, (55, 7793): 661.9062823356531, (55, 7807): 661.7478891208309, (55, 7808): 662.3325896387383, (55, 7831): 622.4142236176975, (55, 7850): 630.5562355080866, (55, 7852): 627.407110729228, (55, 8012): 652.5448280412435, (55, 8125): 684.0676814537766, (55, 8208): 680.8031764790852, (55, 8392): 638.9848925214596, (55, 8651): 518.6679730884209, (55, 9088): 555.7313968692499, (55, 9443): 529.810421331258, (55, 9444): 531.8060836108485, (55, 9828): 505.7433467165238, (55, 9868): 486.90836757111174, (55, 10180): 686.6291293673795, (55, 10256): 716.0744240059107, (55, 10276): 699.8605733289079, (55, 10378): 694.9657193538754, (55, 10676): 690.6121701469127, (55, 10714): 676.0488901718089, (55, 10730): 669.1790697957267, (55, 10862): 739.6213917385409, (55, 10881): 744.1965900472136, (55, 10883): 743.8194570891192, (55, 10885): 738.6045551404459, (55, 10891): 743.2447156499087, (55, 10909): 742.5333702243448, (55, 10911): 742.8566884591049, (55, 10913): 741.9034818122811, (55, 10915): 741.6915531867515, (55, 10919): 742.1903677297466, (55, 11037): 715.5041345529878, (55, 11039): 702.374611660805, (55, 11516): 890.217169625602, (55, 11856): 823.7865046003586, (55, 11857): 824.0900633670568, (55, 11861): 824.0046444502749, (55, 11881): 821.179732697204, (55, 11902): 816.4429275785949, (55, 11911): 814.3053228199626, (55, 11914): 815.5223495907932, (55, 11922): 819.4860391301827, (55, 11924): 820.273446141641, (55, 11926): 818.8331845783155, (55, 11950): 820.114381905032, (55, 11963): 824.7760809934656, (55, 11983): 819.373589405227, (55, 11985): 827.2338010976349, (55, 12009): 824.3483295773534, (55, 12010): 821.5427617843916, (55, 12018): 821.8153546082859, (55, 12020): 822.9963424363779, (55, 12021): 823.3213733253579, (55, 12024): 826.4623313205983, (55, 12025): 825.8080384960742, (55, 12027): 824.9634596022781, (55, 12031): 821.0048863888194, (55, 12032): 822.4126900214076, (55, 12035): 823.6777855406139, (55, 12041): 828.7915675084433, (55, 12045): 783.3729695907538, (55, 12145): 801.1975447884555, (55, 12275): 853.5971105013487, (55, 12294): 842.7312063192994, (55, 12358): 866.2327341755396, (55, 12463): 873.7614657200003, (55, 12465): 873.3141525380578, (55, 12482): 879.9345039375697, (55, 12503): 878.7698409161618, (55, 12506): 880.0346029059351, (55, 12549): 879.8716934465438, (55, 12559): 878.3923214290746, (55, 12569): 878.5165759714878, (55, 12572): 879.5206458233906, (55, 12574): 877.7066086282605, (55, 12576): 881.2836561397645, (55, 12591): 882.5351235688854, (55, 12608): 891.3773541434211, (55, 12696): 879.9240284237352, (55, 12710): 889.152520641138, (55, 12728): 883.5036651210144, (55, 12766): 686.8725849410681, (55, 12771): 683.9310426050288, (55, 12790): 682.6377490450917, (55, 12795): 679.0002650505199, (55, 12797): 671.9475801176351, (55, 12798): 673.5602394798212, (55, 12811): 681.4122544578296, (55, 12830): 677.7625142420063, (55, 12848): 681.1904662077608, (55, 12850): 683.092070854698, (55, 12852): 678.0000205520379, (55, 12854): 676.7746018982288, (55, 12859): 682.950176839821, (55, 12861): 675.3722016840919, (55, 12865): 682.0199372612329, (55, 12866): 681.9892172883306, (55, 12867): 683.9114975814088, (55, 12874): 682.8944817094055, (55, 12875): 684.0828155897093, (55, 12881): 679.5775330722903, (55, 12883): 681.1679374167335, (55, 12885): 684.7544368675366, (55, 12888): 680.8591999219826, (55, 12889): 680.9085925462056, (55, 12892): 682.9276019083449, (55, 12893): 680.5021652431981, (55, 12896): 681.6552673955609, (55, 12906): 681.1492593003645, (55, 13018): 659.3600946731307, (55, 13071): 657.1779890035854, (55, 13131): 656.3239812925173, (55, 13146): 666.6187136719989, (55, 13159): 643.0026273157448, (55, 13193): 655.3978678180009, (55, 13198): 644.7709856876711, (55, 13292): 662.6895534674784, (55, 13296): 671.7299821036056, (55, 13406): 629.010545186677, (55, 13407): 628.0031630518797, (55, 13417): 622.7600384712995, (55, 13418): 623.69526916028, (55, 13438): 633.4226145139138, (55, 13442): 636.0862678273648, (55, 13443): 634.6544954626763, (55, 13764): 494.0552926873101, (55, 13766): 495.8124790194197, (55, 13771): 492.6890918390121, (55, 13783): 494.9755658231761, (55, 13784): 498.33884078365617, (55, 13792): 487.1932374044399, (55, 13824): 493.4870833922657, (55, 14017): 512.2634676515809, (55, 14870): 732.7269909299728, (55, 14997): 602.6871191332434, (55, 15000): 603.877912067885, (55, 15003): 606.0133495753423, (55, 15006): 603.9576532051177, (55, 15007): 605.1835678763459, (55, 15056): 608.1092371062316, (55, 15063): 607.7178565438455, (55, 15069): 608.5222399931241, (55, 15076): 606.083980640234, (55, 15086): 601.2596562061223, (55, 15087): 601.4833819097277, (55, 15111): 597.1013807803, (55, 15116): 599.7218447013736, (55, 15722): 569.4364971483072, (55, 15998): 578.1674879707689, (55, 16073): 234.55508958923045, (55, 16939): 311.4877452092922, (55, 16940): 312.31156359717875, (55, 16951): 307.59501008314544, (55, 16963): 308.4489464907837, (55, 16965): 309.11936636548944, (55, 16969): 306.9788400218776, (55, 16970): 309.42463327683254, (55, 16971): 308.9674564027179, (55, 16973): 307.5791553707861, (55, 16974): 308.0847090671066, (55, 16976): 310.3238924349584, (55, 16978): 310.46226672085135, (55, 16980): 311.66063250053077, (55, 16982): 306.6557899676016, (55, 17045): 203.3667588847442, (55, 17048): 203.40350240698353, (55, 17304): 848.3450952135473, (55, 17305): 845.6639457240461, (55, 17330): 847.2053231959231, (55, 17334): 846.4816314340645, (55, 17343): 848.496390558662, (55, 17345): 844.7476592905601, (55, 17347): 845.9768989691421, (55, 17351): 843.5698785332065, (55, 17372): 845.616456949712, (55, 17373): 848.6230812410776, (55, 17377): 848.6986439477142, (55, 17382): 846.3905961981869, (55, 17383): 847.3742859538439, (55, 17389): 845.8780121111241, (55, 17400): 848.4994742093891, (55, 17401): 848.7159459591326, (55, 17402): 848.4764511223983, (55, 17403): 848.5725415037392, (55, 17440): 843.0935102130327, (55, 17455): 846.9989813160281, (55, 17491): 845.993887187236, (55, 17507): 848.9041633021807, (55, 17509): 850.6759489772863, (55, 17590): 840.8230116332803, (55, 17615): 843.9043506962901, (55, 17642): 844.43803876857, (55, 17643): 843.6874994241941, (55, 17668): 844.2459368020616, (55, 17721): 844.6013920015542, (55, 17754): 858.5124642084311, (55, 17769): 851.2331756455172, (55, 17776): 842.8061306728024, (55, 17804): 853.7467315085736, (55, 17809): 855.1267732392598, (55, 17824): 855.2713114620433, (55, 17837): 846.3818558219617, (55, 17838): 845.5963248050099, (55, 17862): 844.1271752161483, (55, 17866): 847.4981308495526, (55, 17872): 843.7078267803378, (55, 17873): 840.9242526766619, (55, 17881): 845.0568803579662, (55, 17947): 418.85767352841464, (55, 17951): 418.2814497518805, (55, 17953): 419.2723383866634, (55, 17954): 420.029005737973, (55, 17959): 416.8412294499772, (55, 17963): 414.7344448167804, (55, 18000): 415.6145093749304, (55, 18001): 417.07747909692034, (55, 18111): 471.66157353717125, (55, 18148): 475.18604476264034, (55, 18166): 477.6679484709877, (55, 18189): 469.8913173984747, (55, 18239): 849.9473759135377, (55, 18240): 849.7362871141743, (55, 18245): 849.974886450571, (55, 18247): 849.4671868682311, (55, 18251): 849.7326441897009, (55, 18256): 849.7933657788781, (55, 18258): 849.336599978367, (55, 18259): 849.2936042082682, (55, 18260): 849.2803637638968, (55, 18262): 849.3987832985244, (55, 18263): 849.7726472956393, (55, 18264): 849.7719579181207, (55, 18266): 849.3271274966959, (55, 18267): 849.3538946004885, (55, 18268): 849.2941633918473, (55, 18269): 849.3266702145763, (55, 18275): 849.3104574800544, (55, 18285): 849.8491064529264, (55, 18308): 849.4884040690133, (55, 18313): 848.8166793008967, (55, 18314): 848.5166158764506, (55, 18315): 849.864659065835, (55, 18316): 849.5940514244373, (55, 18317): 849.5927984427968, (55, 18320): 849.9703006026531, (55, 18321): 849.8516008446168, (55, 18322): 849.9028080824929, (55, 18324): 850.3175715051707, (55, 18325): 850.8402410368345, (55, 18326): 850.657533247424, (55, 18327): 849.3729942109611, (55, 18329): 851.367060149666, (55, 18330): 850.2922730478756, (55, 18331): 850.0711198008157, (55, 18332): 849.708356552753, (55, 18333): 850.4703275111626, (55, 18336): 850.5679772803485, (55, 18337): 850.91241045898, (55, 18403): 849.1785989505124, (55, 18432): 834.4880705290778, (55, 18451): 844.3933734409658, (55, 18466): 854.7933942185795, (55, 18481): 850.6921662645741, (55, 18483): 850.5079138359247, (55, 18484): 850.3613388580909, (55, 18485): 850.1062881951264, (55, 18486): 851.5332917327482, (55, 18487): 851.0863464901184, (55, 18489): 850.8299665895272, (55, 18490): 851.9970234929735, (55, 18491): 852.3127293031349, (55, 18492): 850.2582673571344, (55, 18493): 851.6403514145657, (55, 18494): 850.5529575908387, (55, 18495): 851.7893542531137, (55, 18496): 851.3076754296158, (55, 18497): 851.1532696127267, (55, 18498): 850.5594005525033, (55, 18499): 850.9816760254729, (55, 18501): 851.0006667308899, (55, 18502): 850.7515133765493, (55, 18503): 850.3366903877821, (55, 18504): 851.2115984666872, (55, 18506): 851.568967501527, (55, 18507): 851.4356560313099, (55, 18508): 851.1011240960487, (55, 18509): 851.2808153364127, (55, 18510): 850.6002481383028, (55, 18511): 852.0968939719576, (55, 18512): 851.4270167757829, (55, 18515): 851.4983318360373, (55, 18516): 852.1236536209245, (55, 18517): 852.0715343137124, (55, 18518): 852.1874854311305, (55, 18519): 851.1645811179056, (55, 18520): 850.801173726126, (55, 18522): 851.9780819036157, (55, 18523): 852.2422466116296, (55, 18532): 852.928549532083, (55, 18535): 851.7086583829821, (55, 18537): 851.0297310561574, (55, 18539): 851.2762159306487, (55, 18540): 851.4657524967978, (55, 18541): 851.8913165799557, (55, 18542): 852.1424847427944, (55, 18543): 850.976734271162, (55, 18546): 851.8700199339129, (55, 18555): 852.9533270901698, (55, 18556): 853.2866465833644, (55, 18565): 853.1188008339635, (55, 18567): 853.8274951812103, (55, 18568): 853.0690495330433, (55, 18577): 857.2227763461366, (55, 18583): 855.9756773265827, (55, 18605): 856.1884680347684, (55, 18608): 854.9839179433937, (55, 18616): 860.1095691401489, (55, 18618): 863.8002967228061, (55, 18625): 861.196667905513, (55, 18645): 857.6583584091067, (55, 18646): 858.9056297903363, (55, 18653): 857.5282575474577, (55, 18654): 860.2631410902635, (55, 18655): 858.7650273821496, (55, 18666): 867.1261365556269, (55, 18837): 833.9199176099247, (55, 18974): 839.7362323093284, (55, 18999): 840.0437405432776, (55, 19000): 840.9811613136789, (55, 19174): 784.0850465562945, (55, 19342): 799.0061282066125, (55, 19455): 800.0867297130627, (55, 19555): 748.8749089911151, (55, 19564): 746.7222631076501, (55, 19573): 745.8251509827219, (55, 19586): 745.7391295957153, (55, 19605): 747.232796947795, (55, 19611): 748.0233547733559, (55, 19614): 748.9796975238941, (55, 19641): 768.2016330086087, (55, 19702): 766.3559107753235, (55, 19713): 765.2539726118921, (55, 19731): 748.6240388850263, (55, 19819): 790.0090709042212, (55, 19893): 804.1642871652444, (55, 19899): 817.6016503865428, (55, 19929): 806.9653875145481, (55, 19951): 831.1301090979317, (55, 19962): 810.3229974501025, (55, 19970): 812.8173779853043, (55, 19971): 813.580017060279, (55, 19972): 812.0225204517668, (55, 19975): 810.6099082561716, (55, 19978): 833.3878558178892, (55, 19987): 833.3805048941986, (55, 19989): 826.7578519920243, (55, 20039): 834.393865744759, (55, 20043): 836.5799558414839, (55, 20047): 833.9487056500158, (55, 20052): 827.095193673033, (55, 20054): 827.9485136628143, (55, 20085): 857.2643774227341, (55, 20104): 859.2075580862191, (55, 20132): 847.8896836296889, (55, 20203): 808.7286125108201, (55, 20280): 807.8739596571139, (55, 20285): 807.9560052470857, (55, 20290): 808.6610041382945, (55, 20297): 806.3107166055772, (55, 20309): 839.4250069084612, (55, 20453): 869.3045004397064, (55, 20485): 791.7056554213013, (55, 20520): 785.6629054213006, (55, 20526): 785.479963909822, (55, 20698): 422.01840713585904, (55, 20868): 357.18019814744747, (55, 21042): 707.4033175253927, (55, 21057): 718.0047996581615, (55, 21066): 714.0142259369876, (55, 21075): 710.2686889666776, (55, 21093): 709.8938246507176, (55, 21098): 719.901751976476, (55, 21127): 709.1761755305336, (55, 21130): 712.0089831763652, (55, 21144): 710.1110393078208, (55, 21146): 708.4737046915122, (55, 21147): 709.4549060969988, (55, 21148): 711.8660211859116, (55, 21153): 701.2175734685064, (55, 21293): 727.2748913456319, (55, 21426): 709.2611432902455, (55, 21442): 717.9645238084555, (55, 21451): 718.877986750919, (55, 21466): 714.3854342828805, (55, 21469): 716.4212247905131, (55, 21471): 713.3202869834314, (55, 21473): 715.1877042004522, (55, 21475): 713.7218467394525, (55, 21482): 717.0923030122617, (55, 21484): 716.9925743580322, (55, 21488): 715.6309194955779, (55, 21494): 714.5655633237105, (55, 21498): 715.8635999150774, (55, 21500): 714.4856183512211, (55, 21514): 721.3671406378068, (55, 21537): 715.9990736746781, (55, 21662): 725.2565927360159, (55, 21691): 718.0302926495721, (55, 21757): 698.730593264163, (55, 21777): 692.1444247371355, (55, 21778): 690.3568833690988, (55, 21779): 692.1535873363613, (55, 21790): 693.2954795269728, (55, 21802): 694.7613149262219, (55, 21824): 697.4111667661118, (55, 21874): 693.5968473597757, (55, 21879): 694.0086200858713, (55, 21983): 693.5025296304508, (55, 22002): 718.2372617595883, (55, 22132): 687.6450029585125, (55, 22261): 535.0127182985384, (55, 22298): 540.709466809652, (55, 22339): 538.7327346252906, (55, 22508): 555.6356824627529, (55, 22841): 51.96355631074535, (55, 22842): 53.01635290590324, (55, 22874): 55.64802727680753, (55, 22941): 52.11564480600655, (55, 22956): 53.61641567405767, (55, 22960): 51.29619479159045, (55, 22968): 66.42787550516164, (55, 22970): 64.5797426322967, (55, 22974): 74.032981597561, (55, 22980): 75.222087655669, (55, 23025): 88.08319149352779, (55, 23028): 90.52867380469208, (55, 23081): 108.7114295307441, (55, 23104): 129.25327710922477, (55, 23147): 87.69276786692281, (55, 23298): 757.3789875864936, (55, 23376): 752.4806115786324, (55, 23381): 753.2740775431402, (55, 23529): 763.5526494191148, (55, 23556): 760.2387370211455, (55, 23718): 751.2736187524581, (55, 24001): 785.7970821017744, (55, 24094): 801.3010636045657, (55, 24129): 806.2516317388233, (55, 24174): 798.5032377285918, (55, 24235): 811.1848372685373, (55, 24259): 814.2648197582879, (55, 24260): 814.1629594574777, (55, 24261): 812.8556698724224, (55, 24305): 819.246092723841, (55, 24306): 820.5488430914867, (55, 24307): 818.8994925022362, (55, 24308): 793.8397687527126, (55, 24498): 826.7722372961879, (55, 24499): 827.0035930846167, (55, 24500): 825.9472588234646, (55, 24668): 813.1684524304532, (55, 24711): 835.8802865067431, (55, 24756): 841.6301400704527, (55, 24788): 842.0791480348365, (55, 24809): 838.849952538122, (55, 24813): 839.6514430057991, (55, 24821): 839.2933949350694, (55, 24825): 839.9681243562255, (55, 24832): 838.3043513047339, (55, 24833): 839.0322045493182, (55, 24835): 839.8816463493484, (55, 24837): 840.7486164523445, (55, 24840): 838.3417662375392, (55, 24841): 839.1555501774169, (55, 24844): 838.5783089002438, (55, 24845): 838.4467527032301, (55, 24846): 839.5022117015413, (55, 24849): 839.9966366834166, (55, 24850): 840.1220568041338, (55, 24863): 828.5432539755928, (55, 24866): 829.7650629543822, (55, 24885): 831.9810374521868, (55, 24886): 832.53496481688, (55, 24889): 833.7835917345593, (55, 24903): 834.1815899779862, (55, 24909): 828.3939331648705, (55, 24999): 879.1985438644182, (55, 25019): 875.9703788308667, (55, 25028): 878.8259248243234, (55, 25137): 819.8407289315879, (55, 25145): 821.8284342452722, (55, 25208): 851.6522919019566, (55, 25233): 849.1368131834206, (55, 25371): 815.3253535080694, (55, 25377): 808.1592963623578, (55, 25828): 701.1660128942667, (55, 25851): 681.4433233695019, (55, 25874): 697.7812370026878, (55, 25898): 708.3208262343998, (55, 25946): 699.3075854745576, (55, 26047): 739.7232665051644, (55, 26066): 760.8539473032191, (55, 26197): 744.4762624119945, (55, 26212): 664.039564758491, (55, 26253): 660.4813484690707, (55, 26254): 661.4269328296275, (55, 26257): 663.9773787576438, (55, 26258): 661.5734561317557, (55, 26260): 662.7112152676858, (55, 26266): 658.3603125168656, (55, 26267): 660.1755031126223, (55, 26271): 660.5915179488869, (55, 26304): 672.0993281304758, (55, 26305): 671.0419906150432, (55, 26363): 700.5787232887307, (55, 26441): 589.7403679833361, (55, 26442): 589.0347721559352, (55, 26450): 590.3225796223493, (55, 26459): 594.2760701793337, (55, 26462): 595.8091501995448, (55, 26467): 592.8505301302985, (55, 26471): 591.6964932202513, (55, 26472): 591.2082324398806, (55, 26473): 590.6854644136321, (55, 26476): 585.4424257908646, (55, 26485): 591.8325042687007, (55, 26493): 589.8096868224393, (55, 26524): 597.0841342370319, (55, 26525): 596.1430629166149, (55, 26556): 592.2871878463235, (55, 26560): 595.6330471234187, (55, 26561): 597.0219732328823, (55, 26564): 591.6775575788863, (55, 26569): 596.109818911811, (55, 26570): 595.133836998773, (55, 26573): 593.2420035761461, (55, 26581): 591.7315148173993, (55, 26583): 592.9104508386089, (55, 26593): 589.7822324467767, (55, 26837): 591.073712020734, (55, 26844): 591.1395273220637, (55, 26863): 587.2284371685156, (55, 26893): 585.8017409885651, (55, 26902): 585.7528029049798, (55, 26905): 589.2131893070476, (55, 26912): 588.0990955995578, (55, 26921): 586.77231758836, (55, 26922): 581.5951943675058, (55, 27212): 667.7727843645457, (55, 27218): 671.0235012717266, (55, 27239): 667.154092527621, (55, 27257): 665.9400702197598, (55, 27274): 666.5111800717045, (55, 27279): 665.2069511845613, (55, 27282): 665.2362997444008, (55, 27283): 667.7224518048544, (55, 27285): 665.730261874738, (55, 27286): 663.5020411299755, (55, 27290): 665.0567124508339, (55, 27295): 666.993090946663, (55, 27300): 667.016979320445, (55, 27344): 661.3068995699745, (55, 27366): 659.9906285981942, (55, 27383): 663.0209340991859, (55, 27398): 666.1569112060884, (55, 27406): 667.1083254840488, (55, 27407): 668.1401246031738, (55, 27426): 676.8520233125573, (55, 27432): 674.2187935532379, (55, 27460): 677.0206690597718, (55, 27523): 639.7994157254526, (55, 27545): 663.0467023623843, (55, 27602): 656.2421730020098, (55, 27606): 657.9872839232145, (55, 27646): 631.7353883236433, (55, 27667): 630.5074265803003, (55, 27672): 631.4698974511864, (55, 27674): 631.0328201623014, (55, 27688): 634.8969535886508, (55, 27692): 630.0997270337722, (55, 27693): 630.0581711872412, (55, 27705): 628.9027841575004, (55, 27712): 627.9371702507267, (55, 27786): 697.9383477141528, (55, 27790): 711.4527466787484, (55, 27791): 713.4229639417837, (55, 27795): 696.4816575117832, (55, 27801): 705.2905350265298, (55, 27813): 696.452923717523, (55, 27816): 699.1123239882687, (55, 27823): 705.7484118794226, (55, 27830): 702.1585679330384, (55, 27884): 622.5188959411192, (55, 27885): 630.4999687773156, (55, 27896): 626.2226136935675, (55, 27919): 627.0192639559439, (55, 27922): 626.3800858855834, (55, 27930): 625.1087238600516, (55, 27934): 624.4297618276012, (55, 27935): 623.5309250310526, (55, 27948): 601.8441332280661, (55, 27951): 619.7250354780432, (55, 28061): 480.2172881224362, (55, 28290): 489.5547943678749, (55, 28292): 484.5014990289121, (55, 28293): 488.15411671469025, (55, 28295): 484.7585015886489, (55, 28296): 487.7701661027672, (55, 28297): 491.8679456539398, (55, 28302): 488.81488497965694, (55, 28310): 245.72373966689585, (55, 28313): 239.6314166066978, (55, 28372): 249.19803086751395, (55, 28398): 248.3466823761355, (55, 28399): 248.143632023295, (55, 28400): 247.17555826506225, (55, 28401): 250.9626479626905, (55, 28445): 237.47832293360375, (55, 28475): 259.9048346841954, (55, 28885): 819.3630730785558, (55, 28886): 818.7062370835024, (55, 28915): 820.8297725872027, (55, 28916): 819.5941038435163, (55, 28917): 819.3419272773504, (55, 28921): 820.9001396044501, (55, 28931): 820.9767070597854, (55, 28945): 820.4483191637079, (55, 28982): 820.2073973483965, (55, 29219): 832.6543876063935, (55, 29228): 827.8814147048058, (55, 29246): 862.202445175954, (55, 29248): 863.0237318709295, (55, 29282): 856.156849671979, (55, 29290): 864.1307034677404, (55, 29291): 863.1602347421922, (55, 29292): 864.2496680368007, (55, 29293): 861.6278135336032, (55, 29294): 864.246788111477, (55, 29298): 862.1585347126364, (55, 29299): 862.2713812341705, (55, 29304): 859.0777157428868, (55, 29317): 852.34778899383, (55, 29323): 851.787053492786, (55, 29330): 855.0877754696103, (55, 29331): 856.4445916794785, (55, 29344): 835.7672790521963, (55, 29445): 786.843247466758, (55, 29724): 24.0, (55, 29738): 24.0, (55, 29745): 24.0, (55, 29748): 24.0, (55, 29750): 24.0, (55, 29759): 24.0, (55, 29772): 24.0, (55, 29781): 24.0, (55, 29784): 24.0, (55, 29790): 24.0, (55, 29811): 24.0, (55, 29817): 27.861731818301514, (55, 29818): 28.208573363423536, (55, 29929): 24.0, (55, 30039): 37.173145207252844, (55, 30066): 47.50686007184344, (55, 30116): 38.85603682626607, (55, 30238): 80.53537706825033, (55, 30248): 63.01041874010202, (55, 30260): 63.66813589970553, (55, 30545): 799.3044777659677, (55, 30733): 747.3104445959692, (55, 30756): 742.847471640673, (55, 30921): 763.1030719315448, (55, 31079): 593.4211257376966, (55, 31149): 596.8577613338306, (55, 31154): 595.4691394899795, (55, 31160): 596.7494309875309, (55, 31163): 594.855945860146, (55, 31189): 582.1373800883213, (55, 31215): 581.4596438706347, (55, 31259): 572.6854350891567, (55, 31262): 571.7061129611692, (55, 31430): 590.6023688743513, (55, 31568): 535.4581448558749, (55, 31751): 581.5594357922611}
    
    # Determine TL and LTL share of demand (effective capacity)
    TL_capacity = TL_share * sum(customers[c][3] for c in customers)
    LTL_capacity = LTL_share * sum(customers[c][3] for c in customers)
    
    # Fix warehouses based on the values of parameters
    fixed_warehouse_ids = []
    for w in warehouses:
        if warehouses[w][0] in fixed_warehouses:
            fixed_warehouse_ids.append(w)
            
    active_warehouses = []
    for w in warehouses:
        if warehouses[w][3] == 1:
            active_warehouses.append(w)
        if w in fixed_warehouse_ids:
            if w not in active_warehouses:
                active_warehouses.append(w)
                
    return warehouses, customers, distance, TL_capacity, LTL_capacity, active_warehouses, costs_TL, costs_LTL, fixed_warehouse_ids

In [5]:
# In this function, we are testing the input paramaters
def test_input(active_warehouses, customers, distance):
    for c in customers:
        for w in active_warehouses:
            if(distance[w,c]>=0):
                pass
            else:
                file.write(f'\nDistance between warehouse {w} and customer {c} is not available or invalid')

    for c in customers.keys():
        if(customers[c][3]>=0):
            pass
        else:
            file.write(f'\nDemand for Customer {c} is not available')

In [6]:
# In this function, we are visualizaing the input data-- the data before the optimization has run
def input_visual(warehouses, customers, active_warehouses):
    warehouse_list = []
    for w in warehouses.keys():
        if w in active_warehouses:
            wh = {
                        'text':'Warehouse-'+str(warehouses[w][0]),
                        'lat':warehouses[w][1],
                        'long':warehouses[w][2],
                        'cnt':10000000,
                        'size' : 30,
                        'color' : 'rgba(0, 100, 0)'
                        }
            warehouse_list.append(wh)    

    customer_list =[] 
    for c in customers.keys():
        cust = {
            'text':'Customer-'+str(customers[c][0]),
            'lat':customers[c][1],
            'long':customers[c][2],
            'cnt':customers[c][3],
            'size' : 3,
            'color' : 'rgb(255, 0, 0)'
        }
        customer_list.append(cust)       

    df = pd.DataFrame.from_records(warehouse_list)
    df['shape'] =  "triangle-down"
    df_cust = pd.DataFrame.from_records(customer_list)
    df_cust['shape'] =  "circle"
    df = df.append(df_cust, ignore_index = True) 

    locations = [ dict(
            type = 'scattergeo',
            lon = df['long'],
            lat = df['lat'],
            hoverinfo = 'text',
            text = df['text'],
            mode = 'markers',
            marker = dict( 
                size=df['size'], 
                color=df['color'],
                symbol = df['shape'],
                line = dict(
                    width=3,
                    color='rgba(68, 68, 68, 0)'
                ),

            ))]

    layout = dict(
            title = "TL_LTL Problem",
            showlegend = False, 
            geo = dict(
                scope='usa',
                projection=dict( type='albers usa' ),
                showland = True,
                landcolor = 'rgb(243, 243, 243)',
                countrycolor = 'rgb(204, 204, 204)',
            ),
        )
    plotly.offline.plot({ "data":locations, "layout":layout}, filename = scenario_name+'_input.html')  

In [7]:
# In this function, we are visualizaing the output data-- the data after the optimization has run
def output_visual(warehouses, customers, df_cu, df_cu_2, scenario_name):   
    
    warehouse_list = []
    for w in list_warehouses_open:
        wh = {
                    'text':'Warehouse-'+str(warehouses[w][0]),
                    'lat':warehouses[w][1],
                    'long':warehouses[w][2],
                    'cnt':10000000,
                    'size' : 30,
                    'color' : 'rgba(0, 100, 0)'
                    }
        warehouse_list.append(wh)    

    customer_list =[] 
    for c in customers.keys():
        cust = {
            'text':'Customer-'+str(customers[c][0]),
            'lat':customers[c][1],
            'long':customers[c][2],
            'cnt':customers[c][3],
            'size' : 3,
            'color' : 'rgb(255, 0, 0)'
        }
        customer_list.append(cust)       

    df = pd.DataFrame.from_records(warehouse_list)
    df['shape'] =  "triangle-down"
    df_cust = pd.DataFrame.from_records(customer_list)
    df_cust['shape'] =  "circle"
    df = df.append(df_cust, ignore_index = True) 
    
    paths = []        
    for i in range( len( df_cu) ):
            paths.append(
                dict(
                    type = 'scattergeo',
                    locationmode = 'USA-states',
                    lon = [ df_cu['Warehouse Longitude'][i], df_cu['Customer Longitude'][i] ],
                    lat = [ df_cu['Warehouse Latitude'][i], df_cu['Customer Latitude'][i] ],
                    mode = 'lines',
                    line = dict(
                        width = 1,
                        color = 'red',
                    ),
                    opacity = 0.8,
                )
            )  
                
    for i in range( len( df_cu_2) ):
        paths.append(
            dict(
                type = 'scattergeo',
                locationmode = 'USA-states',
                lon = [ df_cu_2['Warehouse Longitude'][i], df_cu_2['Customer Longitude'][i] ],
                lat = [ df_cu_2['Warehouse Latitude'][i], df_cu_2['Customer Latitude'][i] ],
                mode = 'lines',
                line = dict(
                    width = 1,
                    color = 'red',
                ),
                opacity = 0.8,
            )
        )  
            

    locations = [ dict(
            type = 'scattergeo',
            lon = df['long'],
            lat = df['lat'],
            hoverinfo = 'text',
            text = df['text'],
            mode = 'markers',
            marker = dict( 
                size=df['size'], 
                color=df['color'],
                symbol = df['shape'],
                line = dict(
                    width=3,
                    color='rgba(68, 68, 68, 0)'
                ),
            ))]
    
    layout = dict(
            title = "TL_LTL Problem Output",
            showlegend = False, 
            geo = dict(
                scope='usa',
                projection=dict( type='albers usa' ),
                showland = True,
                landcolor = 'rgb(243, 243, 243)',
                countrycolor = 'rgb(204, 204, 204)',
            ),
        )

    plotly.offline.plot({"data":locations+paths, "layout":layout},filename=scenario_name+'_output.html')    

In [8]:
# Getting input data
warehouses, customers, distance, TL_capacity, LTL_capacity, active_warehouses, costs_TL, costs_LTL, fixed_warehouse_ids = get_data()

# Opening text and excel file in write mode
file = open(scenario_name+'summary' + '.txt',"w")
writer = pd.ExcelWriter(scenario_name+'_detailed.xlsx')
file.write('Loaded input data.')
print("Loaded input data.")  #Also print to Jupyter

# Testing input data
file.write('\nTesting Input Data')
test_input(active_warehouses, customers, distance)
print("Tested input data.")

# RunCode = ()  #We need some function in here that runs the whole thing.
print("Building and solving the model.")
file.write('\nBuilding the model.')
df_cu, df_cu_2, list_warehouses_open = optimal_warehouses(warehouses, customers, distance, costs_TL, costs_LTL, number_of_whs, fixed_warehouse_ids, distance_band, active_warehouses)

# Printing the maps
if input_map == True:
    input_visual(warehouses, customers, active_warehouses)
if output_map == True:
    output_visual(warehouses, customers, df_cu, df_cu_2, scenario_name)
    
#closing the file
writer.close()
file.close()

Loaded input data.
Tested input data.
Building and solving the model.
Optimization Status Optimal
Total Demand in tons 2582508460000
Objective:  38318549.0164577
Average cost per ton:  0.0 $
Run Time of model in seconds 203.8
The average distance to customers is:  236.7739165944756
The percentage of customers within 300 miles is:  67.38614278150324
